In [1]:
# This function extends sage's number_of_roots_in_interval(a,b) function 
# so that it works with polynomials with non-squarefree polynomials
def numberOfRootsInInterval(f):
	R.<x>=PolynomialRing(QQ)
	ff=R(f)
	if ff.degree() < 1:
		return 0
	g = gcd(ff,ff.derivative())
	if g == 1:
		return ff.number_of_roots_in_interval()
	else:
		return numberOfRootsInInterval(ff/g) + numberOfRootsInInterval(g)


def getCoeffsWeaklyType2(d,clist):
	R.<x>=PolynomialRing(QQ)
	n=len(clist)-1
	coeffLists=[[] for i in range(d-n+1)]
	coeffLists[0]=[clist]
	for i in range(1,d-n+1):
		nn=len(coeffLists[i-1][0])-1
		for j in range(len(coeffLists[i-1])):
			coeffLists[i]+=getCoeffs(coeffLists[i-1][j],2^(nn),nn,d)
	return coeffLists[d-n]


def getCoeffsType2(d,clist):
	R.<x>=PolynomialRing(QQ)
	n=len(clist)-1
	coeffLists=[[] for i in range(d-n+1)]
	coeffLists[0]=[clist]
	for i in range(1,d-n+1):
		for j in range(len(coeffLists[i-1])):
			nn=len(coeffLists[i-1][j])-1
			coeffLists[i]+=getCoeffs(coeffLists[i-1][j],2^(nn+1),nn,d)
	return coeffLists[d-n]
	

def getCoeffs(clist,div,nn,d):
	R.<x>=PolynomialRing(QQ)
	S.<x,y>=PolynomialRing(QQ)
	T.<y>=PolynomialRing(QQ)
	f=R(list(reversed(clist)))
	f*=x^(d-nn)
	for j in range(1,d-nn):
		f=f.derivative(x)
		f/=j
	g = S(f + y)
	g = T(g.discriminant(x))
	roots = g.roots(RealField(1000))
	groots=[]
	for i in range(len(roots)):
	  groots+=[roots[i][0] for j in range(roots[i][1])]
	# groots.sort()
	if len(groots) != (T(g)).degree():
	  print clist
	  print div
	  print nn
	  print "possible error"
	pos=floor(nn/2)
	low=ceil(groots[pos-1])
	high=floor(groots[pos])
	ss=[]
	for j in range(ceil(low/div),floor(high/div)+1):
		if numberOfRootsInInterval(f+div*j) == nn+1:
			ss+=[clist+[div*j]]
	return ss
	
#input: ff and gg are real-rooted polynomials, ff is degree one more than gg
#output: True iff the roots of gg interlace with those of ff
def interlace(ff,gg):
	R.<x>=PolynomialRing(QQ)
	f=R(ff)
	g=R(gg)
	d=gcd(f,g)
	f/=d
	g/=d
	rootsg = (R(g)).roots(RealField(1000))
	groots=[]
	for i in range(len(rootsg)):
		groots+=[rootsg[i][0] for j in range(rootsg[i][1])]
	# groots.sort()
	rootsf = (R(f)).roots(RealField(1000))
	froots=[]
	for i in range(len(rootsf)):
		froots+=[rootsf[i][0] for j in range(rootsf[i][1])]
		# groots.sort()
	for i in range(len(groots)):
		if groots[i] < froots[i]:
			return(False)
		if groots[i] > froots[i+1]:
			return(False)
	return(True)

def listInterlaceReduce(l,f):
	R.<x>=PolynomialRing(QQ)
	ll=[];
	for i in range(len(l)):
		p = R(list(reversed(l[i])))
		if interlace(f,p):
			ll+=[l[i]]
	return(ll);
  
def isType2(f):
	v=f.coefficients(sparse=False)
	v.reverse()
	for i in range(len(v)):
		if v[i]%2^i != 0:
			return False
	return True
  
def listPowerReduce(l,f):
	R.<x>=PolynomialRing(QQ)
	ll=[];
	for i in range(len(l)):
		p = R(list(reversed(l[i])))
		pp=R(f)*p
		if isType2(pp(x-1)):
			ll+=[l[i]]
	return ll
  
def randomSeidel(n):
	m=matrix(n,n)
	for i in range(n):
		for j in range(i+1,n):
			r=ZZ.random_element(0,2)
			r=1-2*r
			m[i,j]=r
			m[j,i]=r
	return m
  
def SeidelCharPolysMod(n,k):
	ll=Set([])
	R.<x> = IntegerModRing(2^k)[]
	if n % 2 == 1:
		ub=2^(binomial(k-2,2)+1)
	else:
		2^(binomial(k-2,2))
	while len(ll) < ub:
		m=randomSeidel(n)
		ll+=Set([R(m.charpoly())])
	return ll
  
def listPowerReduceOdd(lst,f,n,k):
	R.<x>=IntegerModRing(2^k)[]
	ll=[]
	scc=SeidelCharPolysMod(n,k)
	for i in range(len(lst)):
		p = R(list(reversed(lst[i])))
		pp=R(f)*p
		if pp in scc:
			ll+=[lst[i]]
	return ll

#Use precomputed charpoly classes
def listPowerReduceOddPC(lst,f,scc,k):
	R.<x>=IntegerModRing(2^k)[]
	ll=[]
	for i in range(len(lst)):
		p = R(list(reversed(lst[i])))
		pp=R(f)*p
		if pp in scc:
			ll+=[lst[i]]
	return ll

def isAtLeastZero(l):
	for i in range(len(l)):
		if l[i] < 0:
			return False
	return True

import time  
R.<x>=IntegerModRing(2^7)[]

In [2]:
#precompute Seidel char polys classes n=75, e=7
#scc757=SeidelCharPolysMod(75,7)

In [3]:
scc757={x^75 + 41*x^73 + 18*x^72 + 34*x^71 + 120*x^70 + 26*x^69 + 76*x^68 + 5*x^67 + 120*x^66 + 101*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 98*x^7 + 120*x^6 + 90*x^5 + 76*x^4 + 45*x^3 + 120*x^2 + 77*x + 18, x^75 + 41*x^73 + 58*x^72 + 82*x^71 + 24*x^70 + 42*x^69 + 28*x^68 + 85*x^67 + 88*x^66 + 85*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 18*x^7 + 24*x^6 + 106*x^5 + 28*x^4 + 125*x^3 + 88*x^2 + 61*x + 26, x^75 + 41*x^73 + 126*x^72 + 114*x^71 + 24*x^70 + 42*x^69 + 100*x^68 + 117*x^67 + 56*x^66 + 21*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 50*x^7 + 24*x^6 + 106*x^5 + 100*x^4 + 29*x^3 + 56*x^2 + 125*x + 110, x^75 + 41*x^73 + 94*x^72 + 50*x^71 + 88*x^70 + 42*x^69 + 36*x^68 + 53*x^67 + 120*x^66 + 21*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 114*x^7 + 88*x^6 + 106*x^5 + 36*x^4 + 93*x^3 + 120*x^2 + 125*x + 78, x^75 + 41*x^73 + 26*x^72 + 66*x^71 + 8*x^70 + 26*x^69 + 12*x^68 + 37*x^67 + 40*x^66 + 37*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 2*x^7 + 8*x^6 + 90*x^5 + 12*x^4 + 77*x^3 + 40*x^2 + 13*x + 10, x^75 + 41*x^73 + 6*x^72 + 2*x^71 + 24*x^70 + 90*x^69 + 84*x^68 + 101*x^67 + 56*x^66 + 101*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 66*x^7 + 24*x^6 + 26*x^5 + 84*x^4 + 13*x^3 + 56*x^2 + 77*x + 118, x^75 + 41*x^73 + 102*x^72 + 82*x^71 + 40*x^70 + 106*x^69 + 36*x^68 + 85*x^67 + 104*x^66 + 21*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 18*x^7 + 40*x^6 + 42*x^5 + 36*x^4 + 125*x^3 + 104*x^2 + 125*x + 6, x^75 + 41*x^73 + 110*x^72 + 82*x^71 + 88*x^70 + 10*x^69 + 4*x^68 + 21*x^67 + 120*x^66 + 53*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 18*x^7 + 88*x^6 + 74*x^5 + 4*x^4 + 61*x^3 + 120*x^2 + 29*x + 94, x^75 + 41*x^73 + 50*x^72 + 82*x^71 + 104*x^70 + 74*x^69 + 60*x^68 + 21*x^67 + 72*x^66 + 117*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 18*x^7 + 104*x^6 + 10*x^5 + 60*x^4 + 61*x^3 + 72*x^2 + 93*x + 66, x^75 + 41*x^73 + 62*x^72 + 18*x^71 + 24*x^70 + 74*x^69 + 100*x^68 + 85*x^67 + 56*x^66 + 117*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 82*x^7 + 24*x^6 + 10*x^5 + 100*x^4 + 125*x^3 + 56*x^2 + 93*x + 46, x^75 + 41*x^73 + 30*x^72 + 50*x^71 + 120*x^70 + 42*x^69 + 68*x^68 + 53*x^67 + 88*x^66 + 21*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 114*x^7 + 120*x^6 + 106*x^5 + 68*x^4 + 93*x^3 + 88*x^2 + 125*x + 110, x^75 + 41*x^73 + 70*x^72 + 114*x^71 + 8*x^70 + 10*x^69 + 68*x^68 + 53*x^67 + 8*x^66 + 117*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 50*x^7 + 8*x^6 + 74*x^5 + 68*x^4 + 93*x^3 + 8*x^2 + 93*x + 6, x^75 + 41*x^73 + 38*x^72 + 18*x^71 + 72*x^70 + 42*x^69 + 68*x^68 + 21*x^67 + 72*x^66 + 85*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 82*x^7 + 72*x^6 + 106*x^5 + 68*x^4 + 61*x^3 + 72*x^2 + 61*x + 38, x^75 + 41*x^73 + 106*x^72 + 114*x^71 + 24*x^70 + 10*x^69 + 60*x^68 + 53*x^67 + 88*x^66 + 117*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 50*x^7 + 24*x^6 + 74*x^5 + 60*x^4 + 93*x^3 + 88*x^2 + 93*x + 74, x^75 + 41*x^73 + 70*x^72 + 50*x^71 + 40*x^70 + 74*x^69 + 100*x^68 + 117*x^67 + 104*x^66 + 53*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 114*x^7 + 40*x^6 + 10*x^5 + 100*x^4 + 29*x^3 + 104*x^2 + 29*x + 102, x^75 + 41*x^73 + 106*x^72 + 34*x^71 + 104*x^70 + 122*x^69 + 12*x^68 + 69*x^67 + 72*x^66 + 69*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 98*x^7 + 104*x^6 + 58*x^5 + 12*x^4 + 109*x^3 + 72*x^2 + 45*x + 58, x^75 + 41*x^73 + 110*x^72 + 18*x^71 + 120*x^70 + 74*x^69 + 36*x^68 + 85*x^67 + 88*x^66 + 117*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 82*x^7 + 120*x^6 + 10*x^5 + 36*x^4 + 125*x^3 + 88*x^2 + 93*x + 62, x^75 + 41*x^73 + 98*x^72 + 2*x^71 + 24*x^70 + 58*x^69 + 76*x^68 + 37*x^67 + 88*x^66 + 69*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 66*x^7 + 24*x^6 + 122*x^5 + 76*x^4 + 77*x^3 + 88*x^2 + 45*x + 66, x^75 + 41*x^73 + 18*x^72 + 2*x^71 + 88*x^70 + 122*x^69 + 44*x^68 + 37*x^67 + 24*x^66 + 5*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 66*x^7 + 88*x^6 + 58*x^5 + 44*x^4 + 77*x^3 + 24*x^2 + 109*x + 50, x^75 + 41*x^73 + 114*x^72 + 114*x^71 + 8*x^70 + 42*x^69 + 28*x^68 + 117*x^67 + 40*x^66 + 21*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 50*x^7 + 8*x^6 + 106*x^5 + 28*x^4 + 29*x^3 + 40*x^2 + 125*x + 34, x^75 + 41*x^73 + 94*x^72 + 2*x^71 + 8*x^70 + 122*x^69 + 20*x^68 + 37*x^67 + 8*x^66 + 5*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 66*x^7 + 8*x^6 + 58*x^5 + 20*x^4 + 77*x^3 + 8*x^2 + 109*x + 30, x^75 + 41*x^73 + 6*x^72 + 34*x^71 + 24*x^70 + 122*x^69 + 84*x^68 + 69*x^67 + 56*x^66 + 69*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 98*x^7 + 24*x^6 + 58*x^5 + 84*x^4 + 109*x^3 + 56*x^2 + 45*x + 118, x^75 + 41*x^73 + 98*x^72 + 114*x^71 + 104*x^70 + 42*x^69 + 92*x^68 + 117*x^67 + 72*x^66 + 21*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 50*x^7 + 104*x^6 + 106*x^5 + 92*x^4 + 29*x^3 + 72*x^2 + 125*x + 114, x^75 + 41*x^73 + 18*x^72 + 34*x^71 + 88*x^70 + 90*x^69 + 108*x^68 + 5*x^67 + 24*x^66 + 37*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 98*x^7 + 88*x^6 + 26*x^5 + 108*x^4 + 45*x^3 + 24*x^2 + 13*x + 114, x^75 + 41*x^73 + 70*x^72 + 98*x^71 + 120*x^70 + 122*x^69 + 116*x^68 + 5*x^67 + 88*x^66 + 69*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 34*x^7 + 120*x^6 + 58*x^5 + 116*x^4 + 45*x^3 + 88*x^2 + 45*x + 22, x^75 + 41*x^73 + 26*x^72 + 2*x^71 + 104*x^70 + 26*x^69 + 44*x^68 + 101*x^67 + 72*x^66 + 37*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 66*x^7 + 104*x^6 + 90*x^5 + 44*x^4 + 13*x^3 + 72*x^2 + 13*x + 106, x^75 + 41*x^73 + 58*x^72 + 50*x^71 + 56*x^70 + 74*x^69 + 124*x^68 + 117*x^67 + 56*x^66 + 53*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 114*x^7 + 56*x^6 + 10*x^5 + 124*x^4 + 29*x^3 + 56*x^2 + 29*x + 58, x^75 + 41*x^73 + 66*x^72 + 66*x^71 + 56*x^70 + 122*x^69 + 44*x^68 + 101*x^67 + 56*x^66 + 5*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 2*x^7 + 56*x^6 + 58*x^5 + 44*x^4 + 13*x^3 + 56*x^2 + 109*x + 2, x^75 + 41*x^73 + 74*x^72 + 82*x^71 + 24*x^70 + 106*x^69 + 124*x^68 + 85*x^67 + 88*x^66 + 21*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 18*x^7 + 24*x^6 + 42*x^5 + 124*x^4 + 125*x^3 + 88*x^2 + 125*x + 42, x^75 + 41*x^73 + 34*x^72 + 66*x^71 + 56*x^70 + 122*x^69 + 108*x^68 + 101*x^67 + 56*x^66 + 5*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 2*x^7 + 56*x^6 + 58*x^5 + 108*x^4 + 13*x^3 + 56*x^2 + 109*x + 98, x^75 + 41*x^73 + 10*x^72 + 2*x^71 + 72*x^70 + 26*x^69 + 108*x^68 + 101*x^67 + 104*x^66 + 37*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 66*x^7 + 72*x^6 + 90*x^5 + 108*x^4 + 13*x^3 + 104*x^2 + 13*x + 58, x^75 + 41*x^73 + 94*x^72 + 98*x^71 + 40*x^70 + 26*x^69 + 116*x^68 + 69*x^67 + 104*x^66 + 101*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 34*x^7 + 40*x^6 + 90*x^5 + 116*x^4 + 109*x^3 + 104*x^2 + 77*x + 62, x^75 + 41*x^73 + 54*x^72 + 34*x^71 + 56*x^70 + 58*x^69 + 20*x^68 + 69*x^67 + 24*x^66 + 5*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 98*x^7 + 56*x^6 + 122*x^5 + 20*x^4 + 109*x^3 + 24*x^2 + 109*x + 6, x^75 + 41*x^73 + 14*x^72 + 66*x^71 + 40*x^70 + 122*x^69 + 84*x^68 + 101*x^67 + 104*x^66 + 5*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 2*x^7 + 40*x^6 + 58*x^5 + 84*x^4 + 13*x^3 + 104*x^2 + 109*x + 46, x^75 + 41*x^73 + 122*x^72 + 2*x^71 + 8*x^70 + 90*x^69 + 76*x^68 + 101*x^67 + 40*x^66 + 101*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 66*x^7 + 8*x^6 + 26*x^5 + 76*x^4 + 13*x^3 + 40*x^2 + 77*x + 106, x^75 + 41*x^73 + 38*x^72 + 114*x^71 + 72*x^70 + 10*x^69 + 68*x^68 + 53*x^67 + 72*x^66 + 117*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 50*x^7 + 72*x^6 + 74*x^5 + 68*x^4 + 93*x^3 + 72*x^2 + 93*x + 38, x^75 + 41*x^73 + 118*x^72 + 82*x^71 + 40*x^70 + 106*x^69 + 68*x^68 + 85*x^67 + 104*x^66 + 21*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 18*x^7 + 40*x^6 + 42*x^5 + 68*x^4 + 125*x^3 + 104*x^2 + 125*x + 86, x^75 + 41*x^73 + 22*x^72 + 18*x^71 + 40*x^70 + 42*x^69 + 4*x^68 + 21*x^67 + 104*x^66 + 85*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 82*x^7 + 40*x^6 + 106*x^5 + 4*x^4 + 61*x^3 + 104*x^2 + 61*x + 118, x^75 + 41*x^73 + 62*x^72 + 34*x^71 + 8*x^70 + 26*x^69 + 84*x^68 + 5*x^67 + 8*x^66 + 101*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 98*x^7 + 8*x^6 + 90*x^5 + 84*x^4 + 45*x^3 + 8*x^2 + 77*x + 126, x^75 + 41*x^73 + 34*x^72 + 18*x^71 + 72*x^70 + 10*x^69 + 124*x^68 + 85*x^67 + 104*x^66 + 53*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 82*x^7 + 72*x^6 + 74*x^5 + 124*x^4 + 125*x^3 + 104*x^2 + 29*x + 18, x^75 + 41*x^73 + 42*x^72 + 2*x^71 + 72*x^70 + 90*x^69 + 108*x^68 + 101*x^67 + 104*x^66 + 101*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 66*x^7 + 72*x^6 + 26*x^5 + 108*x^4 + 13*x^3 + 104*x^2 + 77*x + 26, x^75 + 41*x^73 + 34*x^72 + 114*x^71 + 104*x^70 + 42*x^69 + 92*x^68 + 117*x^67 + 72*x^66 + 21*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 50*x^7 + 104*x^6 + 106*x^5 + 92*x^4 + 29*x^3 + 72*x^2 + 125*x + 50, x^75 + 41*x^73 + 14*x^72 + 50*x^71 + 56*x^70 + 106*x^69 + 36*x^68 + 53*x^67 + 24*x^66 + 85*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 114*x^7 + 56*x^6 + 42*x^5 + 36*x^4 + 93*x^3 + 24*x^2 + 61*x + 30, x^75 + 41*x^73 + 26*x^72 + 18*x^71 + 120*x^70 + 106*x^69 + 60*x^68 + 21*x^67 + 120*x^66 + 21*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 82*x^7 + 120*x^6 + 42*x^5 + 60*x^4 + 61*x^3 + 120*x^2 + 125*x + 26, x^75 + 41*x^73 + 90*x^72 + 114*x^71 + 120*x^70 + 10*x^69 + 124*x^68 + 53*x^67 + 120*x^66 + 117*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 50*x^7 + 120*x^6 + 74*x^5 + 124*x^4 + 93*x^3 + 120*x^2 + 93*x + 26, x^75 + 41*x^73 + 90*x^72 + 2*x^71 + 104*x^70 + 26*x^69 + 44*x^68 + 101*x^67 + 72*x^66 + 37*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 66*x^7 + 104*x^6 + 90*x^5 + 44*x^4 + 13*x^3 + 72*x^2 + 13*x + 42, x^75 + 41*x^73 + 102*x^72 + 2*x^71 + 88*x^70 + 90*x^69 + 84*x^68 + 101*x^67 + 120*x^66 + 101*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 66*x^7 + 88*x^6 + 26*x^5 + 84*x^4 + 13*x^3 + 120*x^2 + 77*x + 22, x^75 + 41*x^73 + 50*x^72 + 98*x^71 + 24*x^70 + 90*x^69 + 44*x^68 + 69*x^67 + 88*x^66 + 37*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 34*x^7 + 24*x^6 + 26*x^5 + 44*x^4 + 109*x^3 + 88*x^2 + 13*x + 18, x^75 + 41*x^73 + 30*x^72 + 114*x^71 + 24*x^70 + 42*x^69 + 36*x^68 + 117*x^67 + 56*x^66 + 21*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 50*x^7 + 24*x^6 + 106*x^5 + 36*x^4 + 29*x^3 + 56*x^2 + 125*x + 14, x^75 + 41*x^73 + 82*x^72 + 50*x^71 + 72*x^70 + 106*x^69 + 28*x^68 + 53*x^67 + 104*x^66 + 85*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 114*x^7 + 72*x^6 + 42*x^5 + 28*x^4 + 93*x^3 + 104*x^2 + 61*x + 66, x^75 + 41*x^73 + 18*x^72 + 18*x^71 + 72*x^70 + 10*x^69 + 92*x^68 + 85*x^67 + 104*x^66 + 53*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 82*x^7 + 72*x^6 + 74*x^5 + 92*x^4 + 125*x^3 + 104*x^2 + 29*x + 66, x^75 + 41*x^73 + 122*x^72 + 18*x^71 + 56*x^70 + 106*x^69 + 60*x^68 + 21*x^67 + 56*x^66 + 21*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 82*x^7 + 56*x^6 + 42*x^5 + 60*x^4 + 61*x^3 + 56*x^2 + 125*x + 58, x^75 + 41*x^73 + 114*x^72 + 34*x^71 + 24*x^70 + 90*x^69 + 108*x^68 + 5*x^67 + 88*x^66 + 37*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 98*x^7 + 24*x^6 + 26*x^5 + 108*x^4 + 45*x^3 + 88*x^2 + 13*x + 18, x^75 + 41*x^73 + 22*x^72 + 82*x^71 + 8*x^70 + 42*x^69 + 36*x^68 + 85*x^67 + 8*x^66 + 85*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 18*x^7 + 8*x^6 + 106*x^5 + 36*x^4 + 125*x^3 + 8*x^2 + 61*x + 86, x^75 + 41*x^73 + 118*x^72 + 2*x^71 + 24*x^70 + 90*x^69 + 52*x^68 + 101*x^67 + 56*x^66 + 101*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 66*x^7 + 24*x^6 + 26*x^5 + 52*x^4 + 13*x^3 + 56*x^2 + 77*x + 38, x^75 + 41*x^73 + 46*x^72 + 82*x^71 + 88*x^70 + 10*x^69 + 4*x^68 + 21*x^67 + 120*x^66 + 53*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 18*x^7 + 88*x^6 + 74*x^5 + 4*x^4 + 61*x^3 + 120*x^2 + 29*x + 30, x^75 + 41*x^73 + 14*x^72 + 98*x^71 + 40*x^70 + 26*x^69 + 84*x^68 + 69*x^67 + 104*x^66 + 101*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 34*x^7 + 40*x^6 + 90*x^5 + 84*x^4 + 109*x^3 + 104*x^2 + 77*x + 46, x^75 + 41*x^73 + 122*x^72 + 2*x^71 + 104*x^70 + 90*x^69 + 44*x^68 + 101*x^67 + 72*x^66 + 101*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 66*x^7 + 104*x^6 + 26*x^5 + 44*x^4 + 13*x^3 + 72*x^2 + 77*x + 10, x^75 + 41*x^73 + 90*x^72 + 98*x^71 + 8*x^70 + 122*x^69 + 76*x^68 + 5*x^67 + 40*x^66 + 69*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 34*x^7 + 8*x^6 + 58*x^5 + 76*x^4 + 45*x^3 + 40*x^2 + 45*x + 10, x^75 + 41*x^73 + 18*x^72 + 66*x^71 + 120*x^70 + 122*x^69 + 12*x^68 + 101*x^67 + 120*x^66 + 5*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 2*x^7 + 120*x^6 + 58*x^5 + 12*x^4 + 13*x^3 + 120*x^2 + 109*x + 82, x^75 + 41*x^73 + 126*x^72 + 34*x^71 + 8*x^70 + 26*x^69 + 84*x^68 + 5*x^67 + 8*x^66 + 101*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 98*x^7 + 8*x^6 + 90*x^5 + 84*x^4 + 45*x^3 + 8*x^2 + 77*x + 62, x^75 + 41*x^73 + 62*x^72 + 18*x^71 + 120*x^70 + 74*x^69 + 68*x^68 + 85*x^67 + 88*x^66 + 117*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 82*x^7 + 120*x^6 + 10*x^5 + 68*x^4 + 125*x^3 + 88*x^2 + 93*x + 78, x^75 + 41*x^73 + 38*x^72 + 18*x^71 + 104*x^70 + 106*x^69 + 36*x^68 + 21*x^67 + 40*x^66 + 21*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 82*x^7 + 104*x^6 + 42*x^5 + 36*x^4 + 61*x^3 + 40*x^2 + 125*x + 70, x^75 + 41*x^73 + 14*x^72 + 2*x^71 + 8*x^70 + 58*x^69 + 52*x^68 + 37*x^67 + 8*x^66 + 69*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 66*x^7 + 8*x^6 + 122*x^5 + 52*x^4 + 77*x^3 + 8*x^2 + 45*x + 78, x^75 + 41*x^73 + 106*x^72 + 98*x^71 + 8*x^70 + 58*x^69 + 44*x^68 + 5*x^67 + 40*x^66 + 5*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 34*x^7 + 8*x^6 + 122*x^5 + 44*x^4 + 45*x^3 + 40*x^2 + 109*x + 26, x^75 + 41*x^73 + 90*x^72 + 50*x^71 + 56*x^70 + 10*x^69 + 124*x^68 + 117*x^67 + 56*x^66 + 117*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 114*x^7 + 56*x^6 + 74*x^5 + 124*x^4 + 29*x^3 + 56*x^2 + 93*x + 26, x^75 + 41*x^73 + 10*x^72 + 82*x^71 + 88*x^70 + 42*x^69 + 124*x^68 + 85*x^67 + 24*x^66 + 85*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 18*x^7 + 88*x^6 + 106*x^5 + 124*x^4 + 125*x^3 + 24*x^2 + 61*x + 106, x^75 + 41*x^73 + 98*x^72 + 18*x^71 + 104*x^70 + 74*x^69 + 92*x^68 + 85*x^67 + 72*x^66 + 117*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 82*x^7 + 104*x^6 + 10*x^5 + 92*x^4 + 125*x^3 + 72*x^2 + 93*x + 114, x^75 + 41*x^73 + 110*x^72 + 18*x^71 + 56*x^70 + 74*x^69 + 100*x^68 + 85*x^67 + 24*x^66 + 117*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 82*x^7 + 56*x^6 + 10*x^5 + 100*x^4 + 125*x^3 + 24*x^2 + 93*x + 126, x^75 + 41*x^73 + 102*x^72 + 114*x^71 + 40*x^70 + 10*x^69 + 36*x^68 + 53*x^67 + 104*x^66 + 117*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 50*x^7 + 40*x^6 + 74*x^5 + 36*x^4 + 93*x^3 + 104*x^2 + 93*x + 6, x^75 + 41*x^73 + 42*x^72 + 2*x^71 + 40*x^70 + 90*x^69 + 76*x^68 + 101*x^67 + 8*x^66 + 101*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 66*x^7 + 40*x^6 + 26*x^5 + 76*x^4 + 13*x^3 + 8*x^2 + 77*x + 58, x^75 + 41*x^73 + 58*x^72 + 82*x^71 + 88*x^70 + 42*x^69 + 92*x^68 + 85*x^67 + 24*x^66 + 85*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 18*x^7 + 88*x^6 + 106*x^5 + 92*x^4 + 125*x^3 + 24*x^2 + 61*x + 90, x^75 + 41*x^73 + 118*x^72 + 82*x^71 + 104*x^70 + 106*x^69 + 4*x^68 + 85*x^67 + 40*x^66 + 21*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 18*x^7 + 104*x^6 + 42*x^5 + 4*x^4 + 125*x^3 + 40*x^2 + 125*x + 22, x^75 + 41*x^73 + 102*x^72 + 18*x^71 + 104*x^70 + 106*x^69 + 36*x^68 + 21*x^67 + 40*x^66 + 21*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 82*x^7 + 104*x^6 + 42*x^5 + 36*x^4 + 61*x^3 + 40*x^2 + 125*x + 6, x^75 + 41*x^73 + 30*x^72 + 98*x^71 + 72*x^70 + 90*x^69 + 84*x^68 + 69*x^67 + 72*x^66 + 37*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 34*x^7 + 72*x^6 + 26*x^5 + 84*x^4 + 109*x^3 + 72*x^2 + 13*x + 30, x^75 + 41*x^73 + 14*x^72 + 114*x^71 + 120*x^70 + 42*x^69 + 100*x^68 + 117*x^67 + 88*x^66 + 21*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 50*x^7 + 120*x^6 + 106*x^5 + 100*x^4 + 29*x^3 + 88*x^2 + 125*x + 94, x^75 + 41*x^73 + 14*x^72 + 50*x^71 + 24*x^70 + 42*x^69 + 68*x^68 + 53*x^67 + 56*x^66 + 21*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 114*x^7 + 24*x^6 + 106*x^5 + 68*x^4 + 93*x^3 + 56*x^2 + 125*x + 126, x^75 + 41*x^73 + 6*x^72 + 34*x^71 + 56*x^70 + 122*x^69 + 116*x^68 + 69*x^67 + 24*x^66 + 69*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 98*x^7 + 56*x^6 + 58*x^5 + 116*x^4 + 109*x^3 + 24*x^2 + 45*x + 86, x^75 + 41*x^73 + 98*x^72 + 114*x^71 + 72*x^70 + 106*x^69 + 124*x^68 + 117*x^67 + 104*x^66 + 85*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 50*x^7 + 72*x^6 + 42*x^5 + 124*x^4 + 29*x^3 + 104*x^2 + 61*x + 82, x^75 + 41*x^73 + 122*x^72 + 98*x^71 + 72*x^70 + 122*x^69 + 76*x^68 + 5*x^67 + 104*x^66 + 69*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 34*x^7 + 72*x^6 + 58*x^5 + 76*x^4 + 45*x^3 + 104*x^2 + 45*x + 106, x^75 + 41*x^73 + 58*x^72 + 66*x^71 + 104*x^70 + 90*x^69 + 108*x^68 + 37*x^67 + 72*x^66 + 101*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 2*x^7 + 104*x^6 + 26*x^5 + 108*x^4 + 77*x^3 + 72*x^2 + 77*x + 10, x^75 + 41*x^73 + 18*x^72 + 18*x^71 + 104*x^70 + 10*x^69 + 124*x^68 + 85*x^67 + 72*x^66 + 53*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 82*x^7 + 104*x^6 + 74*x^5 + 124*x^4 + 125*x^3 + 72*x^2 + 29*x + 34, x^75 + 41*x^73 + 2*x^72 + 2*x^71 + 88*x^70 + 58*x^69 + 76*x^68 + 37*x^67 + 24*x^66 + 69*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 66*x^7 + 88*x^6 + 122*x^5 + 76*x^4 + 77*x^3 + 24*x^2 + 45*x + 34, x^75 + 41*x^73 + 82*x^72 + 50*x^71 + 104*x^70 + 42*x^69 + 124*x^68 + 53*x^67 + 72*x^66 + 21*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 114*x^7 + 104*x^6 + 106*x^5 + 124*x^4 + 93*x^3 + 72*x^2 + 125*x + 98, x^75 + 41*x^73 + 90*x^72 + 82*x^71 + 120*x^70 + 42*x^69 + 60*x^68 + 85*x^67 + 120*x^66 + 85*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 18*x^7 + 120*x^6 + 106*x^5 + 60*x^4 + 125*x^3 + 120*x^2 + 61*x + 90, x^75 + 41*x^73 + 2*x^72 + 82*x^71 + 104*x^70 + 10*x^69 + 28*x^68 + 21*x^67 + 72*x^66 + 53*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 18*x^7 + 104*x^6 + 74*x^5 + 28*x^4 + 61*x^3 + 72*x^2 + 29*x + 18, x^75 + 41*x^73 + 26*x^72 + 18*x^71 + 56*x^70 + 42*x^69 + 60*x^68 + 21*x^67 + 56*x^66 + 85*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 82*x^7 + 56*x^6 + 106*x^5 + 60*x^4 + 61*x^3 + 56*x^2 + 61*x + 26, x^75 + 41*x^73 + 70*x^72 + 18*x^71 + 8*x^70 + 42*x^69 + 68*x^68 + 21*x^67 + 8*x^66 + 85*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 82*x^7 + 8*x^6 + 106*x^5 + 68*x^4 + 61*x^3 + 8*x^2 + 61*x + 6, x^75 + 41*x^73 + 34*x^72 + 114*x^71 + 8*x^70 + 42*x^69 + 124*x^68 + 117*x^67 + 40*x^66 + 21*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 50*x^7 + 8*x^6 + 106*x^5 + 124*x^4 + 29*x^3 + 40*x^2 + 125*x + 18, x^75 + 41*x^73 + 74*x^72 + 82*x^71 + 56*x^70 + 42*x^69 + 92*x^68 + 85*x^67 + 56*x^66 + 85*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 18*x^7 + 56*x^6 + 106*x^5 + 92*x^4 + 125*x^3 + 56*x^2 + 61*x + 74, x^75 + 41*x^73 + 94*x^72 + 18*x^71 + 56*x^70 + 10*x^69 + 4*x^68 + 85*x^67 + 24*x^66 + 53*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 82*x^7 + 56*x^6 + 74*x^5 + 4*x^4 + 125*x^3 + 24*x^2 + 29*x + 110, x^75 + 41*x^73 + 50*x^72 + 2*x^71 + 56*x^70 + 58*x^69 + 12*x^68 + 37*x^67 + 56*x^66 + 69*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 66*x^7 + 56*x^6 + 122*x^5 + 12*x^4 + 77*x^3 + 56*x^2 + 45*x + 50, x^75 + 41*x^73 + 94*x^72 + 50*x^71 + 56*x^70 + 42*x^69 + 4*x^68 + 53*x^67 + 24*x^66 + 21*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 114*x^7 + 56*x^6 + 106*x^5 + 4*x^4 + 93*x^3 + 24*x^2 + 125*x + 110, x^75 + 41*x^73 + 22*x^72 + 98*x^71 + 56*x^70 + 122*x^69 + 84*x^68 + 5*x^67 + 24*x^66 + 69*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 34*x^7 + 56*x^6 + 58*x^5 + 84*x^4 + 45*x^3 + 24*x^2 + 45*x + 102, x^75 + 41*x^73 + 22*x^72 + 66*x^71 + 24*x^70 + 90*x^69 + 52*x^68 + 37*x^67 + 56*x^66 + 101*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 2*x^7 + 24*x^6 + 26*x^5 + 52*x^4 + 77*x^3 + 56*x^2 + 77*x + 6, x^75 + 41*x^73 + 110*x^72 + 50*x^71 + 88*x^70 + 42*x^69 + 68*x^68 + 53*x^67 + 120*x^66 + 21*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 114*x^7 + 88*x^6 + 106*x^5 + 68*x^4 + 93*x^3 + 120*x^2 + 125*x + 30, x^75 + 41*x^73 + 78*x^72 + 50*x^71 + 120*x^70 + 106*x^69 + 100*x^68 + 53*x^67 + 88*x^66 + 85*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 114*x^7 + 120*x^6 + 42*x^5 + 100*x^4 + 93*x^3 + 88*x^2 + 61*x + 30, x^75 + 41*x^73 + 42*x^72 + 2*x^71 + 40*x^70 + 26*x^69 + 12*x^68 + 101*x^67 + 8*x^66 + 37*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 66*x^7 + 40*x^6 + 90*x^5 + 12*x^4 + 13*x^3 + 8*x^2 + 13*x + 122, x^75 + 41*x^73 + 94*x^72 + 18*x^71 + 120*x^70 + 74*x^69 + 4*x^68 + 85*x^67 + 88*x^66 + 117*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 82*x^7 + 120*x^6 + 10*x^5 + 4*x^4 + 125*x^3 + 88*x^2 + 93*x + 110, x^75 + 41*x^73 + 62*x^72 + 114*x^71 + 88*x^70 + 42*x^69 + 36*x^68 + 117*x^67 + 120*x^66 + 21*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 50*x^7 + 88*x^6 + 106*x^5 + 36*x^4 + 29*x^3 + 120*x^2 + 125*x + 110, x^75 + 41*x^73 + 110*x^72 + 98*x^71 + 72*x^70 + 26*x^69 + 52*x^68 + 69*x^67 + 72*x^66 + 101*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 34*x^7 + 72*x^6 + 90*x^5 + 52*x^4 + 109*x^3 + 72*x^2 + 77*x + 110, x^75 + 41*x^73 + 30*x^72 + 66*x^71 + 40*x^70 + 58*x^69 + 52*x^68 + 101*x^67 + 104*x^66 + 69*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 2*x^7 + 40*x^6 + 122*x^5 + 52*x^4 + 13*x^3 + 104*x^2 + 45*x + 62, x^75 + 41*x^73 + 38*x^72 + 50*x^71 + 72*x^70 + 74*x^69 + 68*x^68 + 117*x^67 + 72*x^66 + 53*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 114*x^7 + 72*x^6 + 10*x^5 + 68*x^4 + 29*x^3 + 72*x^2 + 29*x + 38, x^75 + 41*x^73 + 70*x^72 + 18*x^71 + 40*x^70 + 106*x^69 + 36*x^68 + 21*x^67 + 104*x^66 + 21*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 82*x^7 + 40*x^6 + 42*x^5 + 36*x^4 + 61*x^3 + 104*x^2 + 125*x + 38, x^75 + 41*x^73 + 78*x^72 + 114*x^71 + 88*x^70 + 106*x^69 + 4*x^68 + 117*x^67 + 120*x^66 + 85*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 50*x^7 + 88*x^6 + 42*x^5 + 4*x^4 + 29*x^3 + 120*x^2 + 61*x + 126, x^75 + 41*x^73 + 34*x^72 + 50*x^71 + 72*x^70 + 42*x^69 + 124*x^68 + 53*x^67 + 104*x^66 + 21*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 114*x^7 + 72*x^6 + 106*x^5 + 124*x^4 + 93*x^3 + 104*x^2 + 125*x + 18, x^75 + 41*x^73 + 46*x^72 + 50*x^71 + 120*x^70 + 106*x^69 + 36*x^68 + 53*x^67 + 88*x^66 + 85*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 114*x^7 + 120*x^6 + 42*x^5 + 36*x^4 + 93*x^3 + 88*x^2 + 61*x + 126, x^75 + 41*x^73 + 102*x^72 + 34*x^71 + 56*x^70 + 122*x^69 + 52*x^68 + 69*x^67 + 24*x^66 + 69*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 98*x^7 + 56*x^6 + 58*x^5 + 52*x^4 + 109*x^3 + 24*x^2 + 45*x + 54, x^75 + 41*x^73 + 46*x^72 + 82*x^71 + 120*x^70 + 74*x^69 + 100*x^68 + 21*x^67 + 88*x^66 + 117*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 18*x^7 + 120*x^6 + 10*x^5 + 100*x^4 + 61*x^3 + 88*x^2 + 93*x + 62, x^75 + 41*x^73 + 2*x^72 + 50*x^71 + 8*x^70 + 106*x^69 + 60*x^68 + 53*x^67 + 40*x^66 + 85*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 114*x^7 + 8*x^6 + 42*x^5 + 60*x^4 + 93*x^3 + 40*x^2 + 61*x + 114, x^75 + 41*x^73 + 30*x^72 + 2*x^71 + 72*x^70 + 58*x^69 + 20*x^68 + 37*x^67 + 72*x^66 + 69*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 66*x^7 + 72*x^6 + 122*x^5 + 20*x^4 + 77*x^3 + 72*x^2 + 45*x + 94, x^75 + 41*x^73 + 114*x^72 + 2*x^71 + 120*x^70 + 58*x^69 + 76*x^68 + 37*x^67 + 120*x^66 + 69*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 66*x^7 + 120*x^6 + 122*x^5 + 76*x^4 + 77*x^3 + 120*x^2 + 45*x + 50, x^75 + 41*x^73 + 118*x^72 + 50*x^71 + 104*x^70 + 10*x^69 + 68*x^68 + 117*x^67 + 40*x^66 + 117*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 114*x^7 + 104*x^6 + 74*x^5 + 68*x^4 + 29*x^3 + 40*x^2 + 93*x + 86, x^75 + 41*x^73 + 22*x^72 + 98*x^71 + 24*x^70 + 122*x^69 + 52*x^68 + 5*x^67 + 56*x^66 + 69*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 34*x^7 + 24*x^6 + 58*x^5 + 52*x^4 + 45*x^3 + 56*x^2 + 45*x + 6, x^75 + 41*x^73 + 46*x^72 + 50*x^71 + 88*x^70 + 42*x^69 + 68*x^68 + 53*x^67 + 120*x^66 + 21*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 114*x^7 + 88*x^6 + 106*x^5 + 68*x^4 + 93*x^3 + 120*x^2 + 125*x + 94, x^75 + 41*x^73 + 2*x^72 + 82*x^71 + 72*x^70 + 10*x^69 + 124*x^68 + 21*x^67 + 104*x^66 + 53*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 18*x^7 + 72*x^6 + 74*x^5 + 124*x^4 + 61*x^3 + 104*x^2 + 29*x + 50, x^75 + 41*x^73 + 126*x^72 + 66*x^71 + 40*x^70 + 122*x^69 + 52*x^68 + 101*x^67 + 104*x^66 + 5*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 2*x^7 + 40*x^6 + 58*x^5 + 52*x^4 + 13*x^3 + 104*x^2 + 109*x + 94, x^75 + 41*x^73 + 2*x^72 + 66*x^71 + 24*x^70 + 122*x^69 + 12*x^68 + 101*x^67 + 88*x^66 + 5*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 2*x^7 + 24*x^6 + 58*x^5 + 12*x^4 + 13*x^3 + 88*x^2 + 109*x + 98, x^75 + 41*x^73 + 30*x^72 + 2*x^71 + 104*x^70 + 122*x^69 + 116*x^68 + 37*x^67 + 40*x^66 + 5*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 66*x^7 + 104*x^6 + 58*x^5 + 116*x^4 + 77*x^3 + 40*x^2 + 109*x + 126, x^75 + 41*x^73 + 86*x^72 + 18*x^71 + 72*x^70 + 106*x^69 + 100*x^68 + 21*x^67 + 72*x^66 + 21*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 82*x^7 + 72*x^6 + 42*x^5 + 100*x^4 + 61*x^3 + 72*x^2 + 125*x + 86, x^75 + 41*x^73 + 90*x^72 + 18*x^71 + 88*x^70 + 106*x^69 + 28*x^68 + 21*x^67 + 24*x^66 + 21*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 82*x^7 + 88*x^6 + 42*x^5 + 28*x^4 + 61*x^3 + 24*x^2 + 125*x + 122, x^75 + 41*x^73 + 62*x^72 + 50*x^71 + 24*x^70 + 106*x^69 + 100*x^68 + 53*x^67 + 56*x^66 + 85*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 114*x^7 + 24*x^6 + 42*x^5 + 100*x^4 + 93*x^3 + 56*x^2 + 61*x + 46, x^75 + 41*x^73 + 26*x^72 + 98*x^71 + 40*x^70 + 122*x^69 + 108*x^68 + 5*x^67 + 8*x^66 + 69*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 34*x^7 + 40*x^6 + 58*x^5 + 108*x^4 + 45*x^3 + 8*x^2 + 45*x + 42, x^75 + 41*x^73 + 26*x^72 + 34*x^71 + 8*x^70 + 58*x^69 + 76*x^68 + 69*x^67 + 40*x^66 + 5*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 98*x^7 + 8*x^6 + 122*x^5 + 76*x^4 + 109*x^3 + 40*x^2 + 109*x + 74, x^75 + 41*x^73 + 22*x^72 + 2*x^71 + 24*x^70 + 90*x^69 + 116*x^68 + 101*x^67 + 56*x^66 + 101*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 66*x^7 + 24*x^6 + 26*x^5 + 116*x^4 + 13*x^3 + 56*x^2 + 77*x + 70, x^75 + 41*x^73 + 14*x^72 + 114*x^71 + 88*x^70 + 106*x^69 + 4*x^68 + 117*x^67 + 120*x^66 + 85*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 50*x^7 + 88*x^6 + 42*x^5 + 4*x^4 + 29*x^3 + 120*x^2 + 61*x + 62, x^75 + 41*x^73 + 98*x^72 + 2*x^71 + 56*x^70 + 122*x^69 + 44*x^68 + 37*x^67 + 56*x^66 + 5*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 66*x^7 + 56*x^6 + 58*x^5 + 44*x^4 + 77*x^3 + 56*x^2 + 109*x + 98, x^75 + 41*x^73 + 22*x^72 + 2*x^71 + 88*x^70 + 90*x^69 + 52*x^68 + 101*x^67 + 120*x^66 + 101*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 66*x^7 + 88*x^6 + 26*x^5 + 52*x^4 + 13*x^3 + 120*x^2 + 77*x + 6, x^75 + 41*x^73 + 86*x^72 + 114*x^71 + 8*x^70 + 74*x^69 + 36*x^68 + 53*x^67 + 8*x^66 + 53*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 50*x^7 + 8*x^6 + 10*x^5 + 36*x^4 + 93*x^3 + 8*x^2 + 29*x + 22, x^75 + 41*x^73 + 90*x^72 + 2*x^71 + 72*x^70 + 26*x^69 + 12*x^68 + 101*x^67 + 104*x^66 + 37*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 66*x^7 + 72*x^6 + 90*x^5 + 12*x^4 + 13*x^3 + 104*x^2 + 13*x + 74, x^75 + 41*x^73 + 110*x^72 + 66*x^71 + 8*x^70 + 58*x^69 + 52*x^68 + 101*x^67 + 8*x^66 + 69*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 2*x^7 + 8*x^6 + 122*x^5 + 52*x^4 + 13*x^3 + 8*x^2 + 45*x + 110, x^75 + 41*x^73 + 78*x^72 + 34*x^71 + 40*x^70 + 26*x^69 + 20*x^68 + 5*x^67 + 104*x^66 + 101*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 98*x^7 + 40*x^6 + 90*x^5 + 20*x^4 + 45*x^3 + 104*x^2 + 77*x + 46, x^75 + 41*x^73 + 10*x^72 + 66*x^71 + 104*x^70 + 26*x^69 + 76*x^68 + 37*x^67 + 72*x^66 + 37*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 2*x^7 + 104*x^6 + 90*x^5 + 76*x^4 + 77*x^3 + 72*x^2 + 13*x + 90, x^75 + 41*x^73 + 6*x^72 + 98*x^71 + 120*x^70 + 122*x^69 + 116*x^68 + 5*x^67 + 88*x^66 + 69*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 34*x^7 + 120*x^6 + 58*x^5 + 116*x^4 + 45*x^3 + 88*x^2 + 45*x + 86, x^75 + 41*x^73 + 66*x^72 + 50*x^71 + 8*x^70 + 106*x^69 + 60*x^68 + 53*x^67 + 40*x^66 + 85*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 114*x^7 + 8*x^6 + 42*x^5 + 60*x^4 + 93*x^3 + 40*x^2 + 61*x + 50, x^75 + 41*x^73 + 126*x^72 + 114*x^71 + 88*x^70 + 42*x^69 + 36*x^68 + 117*x^67 + 120*x^66 + 21*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 50*x^7 + 88*x^6 + 106*x^5 + 36*x^4 + 29*x^3 + 120*x^2 + 125*x + 46, x^75 + 41*x^73 + 70*x^72 + 114*x^71 + 104*x^70 + 10*x^69 + 36*x^68 + 53*x^67 + 40*x^66 + 117*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 50*x^7 + 104*x^6 + 74*x^5 + 36*x^4 + 93*x^3 + 40*x^2 + 93*x + 38, x^75 + 41*x^73 + 70*x^72 + 2*x^71 + 88*x^70 + 26*x^69 + 84*x^68 + 101*x^67 + 120*x^66 + 37*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 66*x^7 + 88*x^6 + 90*x^5 + 84*x^4 + 13*x^3 + 120*x^2 + 13*x + 54, x^75 + 41*x^73 + 26*x^72 + 2*x^71 + 40*x^70 + 90*x^69 + 44*x^68 + 101*x^67 + 8*x^66 + 101*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 66*x^7 + 40*x^6 + 26*x^5 + 44*x^4 + 13*x^3 + 8*x^2 + 77*x + 106, x^75 + 41*x^73 + 50*x^72 + 2*x^71 + 24*x^70 + 122*x^69 + 44*x^68 + 37*x^67 + 88*x^66 + 5*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 66*x^7 + 24*x^6 + 58*x^5 + 44*x^4 + 77*x^3 + 88*x^2 + 109*x + 18, x^75 + 41*x^73 + 2*x^72 + 2*x^71 + 56*x^70 + 58*x^69 + 44*x^68 + 37*x^67 + 56*x^66 + 69*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 66*x^7 + 56*x^6 + 122*x^5 + 44*x^4 + 77*x^3 + 56*x^2 + 45*x + 66, x^75 + 41*x^73 + 114*x^72 + 114*x^71 + 40*x^70 + 42*x^69 + 60*x^68 + 117*x^67 + 8*x^66 + 21*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 50*x^7 + 40*x^6 + 106*x^5 + 60*x^4 + 29*x^3 + 8*x^2 + 125*x + 2, x^75 + 41*x^73 + 102*x^72 + 34*x^71 + 24*x^70 + 122*x^69 + 20*x^68 + 69*x^67 + 56*x^66 + 69*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 98*x^7 + 24*x^6 + 58*x^5 + 20*x^4 + 109*x^3 + 56*x^2 + 45*x + 86, x^75 + 41*x^73 + 122*x^72 + 82*x^71 + 120*x^70 + 106*x^69 + 60*x^68 + 85*x^67 + 120*x^66 + 21*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 18*x^7 + 120*x^6 + 42*x^5 + 60*x^4 + 125*x^3 + 120*x^2 + 125*x + 58, x^75 + 41*x^73 + 114*x^72 + 98*x^71 + 120*x^70 + 90*x^69 + 12*x^68 + 69*x^67 + 120*x^66 + 37*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 34*x^7 + 120*x^6 + 26*x^5 + 12*x^4 + 109*x^3 + 120*x^2 + 13*x + 114, x^75 + 41*x^73 + 50*x^72 + 114*x^71 + 8*x^70 + 106*x^69 + 92*x^68 + 117*x^67 + 40*x^66 + 85*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 50*x^7 + 8*x^6 + 42*x^5 + 92*x^4 + 29*x^3 + 40*x^2 + 61*x + 34, x^75 + 41*x^73 + 110*x^72 + 66*x^71 + 72*x^70 + 58*x^69 + 116*x^68 + 101*x^67 + 72*x^66 + 69*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 2*x^7 + 72*x^6 + 122*x^5 + 116*x^4 + 13*x^3 + 72*x^2 + 45*x + 46, x^75 + 41*x^73 + 86*x^72 + 34*x^71 + 24*x^70 + 122*x^69 + 116*x^68 + 69*x^67 + 56*x^66 + 69*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 98*x^7 + 24*x^6 + 58*x^5 + 116*x^4 + 109*x^3 + 56*x^2 + 45*x + 6, x^75 + 41*x^73 + 54*x^72 + 82*x^71 + 8*x^70 + 106*x^69 + 36*x^68 + 85*x^67 + 8*x^66 + 21*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 18*x^7 + 8*x^6 + 42*x^5 + 36*x^4 + 125*x^3 + 8*x^2 + 125*x + 54, x^75 + 41*x^73 + 110*x^72 + 18*x^71 + 88*x^70 + 10*x^69 + 68*x^68 + 85*x^67 + 120*x^66 + 53*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 82*x^7 + 88*x^6 + 74*x^5 + 68*x^4 + 125*x^3 + 120*x^2 + 29*x + 30, x^75 + 41*x^73 + 74*x^72 + 18*x^71 + 120*x^70 + 42*x^69 + 92*x^68 + 21*x^67 + 120*x^66 + 85*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 82*x^7 + 120*x^6 + 106*x^5 + 92*x^4 + 61*x^3 + 120*x^2 + 61*x + 74, x^75 + 41*x^73 + 58*x^72 + 66*x^71 + 104*x^70 + 26*x^69 + 44*x^68 + 37*x^67 + 72*x^66 + 37*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 2*x^7 + 104*x^6 + 90*x^5 + 44*x^4 + 77*x^3 + 72*x^2 + 13*x + 74, x^75 + 41*x^73 + 6*x^72 + 50*x^71 + 72*x^70 + 10*x^69 + 68*x^68 + 117*x^67 + 72*x^66 + 117*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 114*x^7 + 72*x^6 + 74*x^5 + 68*x^4 + 29*x^3 + 72*x^2 + 93*x + 70, x^75 + 41*x^73 + 42*x^72 + 50*x^71 + 24*x^70 + 10*x^69 + 124*x^68 + 117*x^67 + 88*x^66 + 117*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 114*x^7 + 24*x^6 + 74*x^5 + 124*x^4 + 29*x^3 + 88*x^2 + 93*x + 74, x^75 + 41*x^73 + 90*x^72 + 82*x^71 + 56*x^70 + 42*x^69 + 124*x^68 + 85*x^67 + 56*x^66 + 85*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 18*x^7 + 56*x^6 + 106*x^5 + 124*x^4 + 125*x^3 + 56*x^2 + 61*x + 26, x^75 + 41*x^73 + 110*x^72 + 18*x^71 + 120*x^70 + 10*x^69 + 100*x^68 + 85*x^67 + 88*x^66 + 53*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 82*x^7 + 120*x^6 + 74*x^5 + 100*x^4 + 125*x^3 + 88*x^2 + 29*x + 126, x^75 + 41*x^73 + 82*x^72 + 66*x^71 + 24*x^70 + 122*x^69 + 44*x^68 + 101*x^67 + 88*x^66 + 5*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 2*x^7 + 24*x^6 + 58*x^5 + 44*x^4 + 13*x^3 + 88*x^2 + 109*x + 114, x^75 + 41*x^73 + 6*x^72 + 98*x^71 + 24*x^70 + 58*x^69 + 84*x^68 + 5*x^67 + 56*x^66 + 5*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 34*x^7 + 24*x^6 + 122*x^5 + 84*x^4 + 45*x^3 + 56*x^2 + 109*x + 118, x^75 + 41*x^73 + 66*x^72 + 114*x^71 + 72*x^70 + 42*x^69 + 124*x^68 + 117*x^67 + 104*x^66 + 21*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 50*x^7 + 72*x^6 + 106*x^5 + 124*x^4 + 29*x^3 + 104*x^2 + 125*x + 114, x^75 + 41*x^73 + 42*x^72 + 98*x^71 + 40*x^70 + 122*x^69 + 12*x^68 + 5*x^67 + 8*x^66 + 69*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 34*x^7 + 40*x^6 + 58*x^5 + 12*x^4 + 45*x^3 + 8*x^2 + 45*x + 122, x^75 + 41*x^73 + 90*x^72 + 2*x^71 + 104*x^70 + 90*x^69 + 108*x^68 + 101*x^67 + 72*x^66 + 101*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 66*x^7 + 104*x^6 + 26*x^5 + 108*x^4 + 13*x^3 + 72*x^2 + 77*x + 106, x^75 + 41*x^73 + 6*x^72 + 66*x^71 + 56*x^70 + 90*x^69 + 52*x^68 + 37*x^67 + 24*x^66 + 101*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 2*x^7 + 56*x^6 + 26*x^5 + 52*x^4 + 77*x^3 + 24*x^2 + 77*x + 22, x^75 + 41*x^73 + 14*x^72 + 66*x^71 + 72*x^70 + 122*x^69 + 116*x^68 + 101*x^67 + 72*x^66 + 5*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 2*x^7 + 72*x^6 + 58*x^5 + 116*x^4 + 13*x^3 + 72*x^2 + 109*x + 14, x^75 + 41*x^73 + 126*x^72 + 2*x^71 + 8*x^70 + 58*x^69 + 20*x^68 + 37*x^67 + 8*x^66 + 69*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 66*x^7 + 8*x^6 + 122*x^5 + 20*x^4 + 77*x^3 + 8*x^2 + 45*x + 126, x^75 + 41*x^73 + 114*x^72 + 98*x^71 + 56*x^70 + 26*x^69 + 12*x^68 + 69*x^67 + 56*x^66 + 101*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 34*x^7 + 56*x^6 + 90*x^5 + 12*x^4 + 109*x^3 + 56*x^2 + 77*x + 114, x^75 + 41*x^73 + 86*x^72 + 66*x^71 + 120*x^70 + 90*x^69 + 20*x^68 + 37*x^67 + 88*x^66 + 101*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 2*x^7 + 120*x^6 + 26*x^5 + 20*x^4 + 77*x^3 + 88*x^2 + 77*x + 102, x^75 + 41*x^73 + 74*x^72 + 2*x^71 + 40*x^70 + 26*x^69 + 76*x^68 + 101*x^67 + 8*x^66 + 37*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 66*x^7 + 40*x^6 + 90*x^5 + 76*x^4 + 13*x^3 + 8*x^2 + 13*x + 26, x^75 + 41*x^73 + 26*x^72 + 114*x^71 + 24*x^70 + 10*x^69 + 28*x^68 + 53*x^67 + 88*x^66 + 117*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 50*x^7 + 24*x^6 + 74*x^5 + 28*x^4 + 93*x^3 + 88*x^2 + 93*x + 58, x^75 + 41*x^73 + 38*x^72 + 114*x^71 + 40*x^70 + 10*x^69 + 36*x^68 + 53*x^67 + 104*x^66 + 117*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 50*x^7 + 40*x^6 + 74*x^5 + 36*x^4 + 93*x^3 + 104*x^2 + 93*x + 70, x^75 + 41*x^73 + 18*x^72 + 66*x^71 + 120*x^70 + 58*x^69 + 76*x^68 + 101*x^67 + 120*x^66 + 69*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 2*x^7 + 120*x^6 + 122*x^5 + 76*x^4 + 13*x^3 + 120*x^2 + 45*x + 18, x^75 + 41*x^73 + 30*x^72 + 18*x^71 + 56*x^70 + 74*x^69 + 68*x^68 + 85*x^67 + 24*x^66 + 117*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 82*x^7 + 56*x^6 + 10*x^5 + 68*x^4 + 125*x^3 + 24*x^2 + 93*x + 110, x^75 + 41*x^73 + 66*x^72 + 2*x^71 + 56*x^70 + 58*x^69 + 44*x^68 + 37*x^67 + 56*x^66 + 69*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 66*x^7 + 56*x^6 + 122*x^5 + 44*x^4 + 77*x^3 + 56*x^2 + 45*x + 2, x^75 + 41*x^73 + 62*x^72 + 34*x^71 + 8*x^70 + 90*x^69 + 20*x^68 + 5*x^67 + 8*x^66 + 37*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 98*x^7 + 8*x^6 + 26*x^5 + 20*x^4 + 45*x^3 + 8*x^2 + 13*x + 62, x^75 + 41*x^73 + 26*x^72 + 66*x^71 + 104*x^70 + 90*x^69 + 44*x^68 + 37*x^67 + 72*x^66 + 101*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 2*x^7 + 104*x^6 + 26*x^5 + 44*x^4 + 77*x^3 + 72*x^2 + 77*x + 106, x^75 + 41*x^73 + 18*x^72 + 114*x^71 + 40*x^70 + 42*x^69 + 124*x^68 + 117*x^67 + 8*x^66 + 21*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 50*x^7 + 40*x^6 + 106*x^5 + 124*x^4 + 29*x^3 + 8*x^2 + 125*x + 34, x^75 + 41*x^73 + 6*x^72 + 2*x^71 + 56*x^70 + 26*x^69 + 52*x^68 + 101*x^67 + 24*x^66 + 37*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 66*x^7 + 56*x^6 + 90*x^5 + 52*x^4 + 13*x^3 + 24*x^2 + 13*x + 22, x^75 + 41*x^73 + 22*x^72 + 34*x^71 + 24*x^70 + 58*x^69 + 52*x^68 + 69*x^67 + 56*x^66 + 5*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 98*x^7 + 24*x^6 + 122*x^5 + 52*x^4 + 109*x^3 + 56*x^2 + 109*x + 6, x^75 + 41*x^73 + 18*x^72 + 2*x^71 + 56*x^70 + 122*x^69 + 12*x^68 + 37*x^67 + 56*x^66 + 5*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 66*x^7 + 56*x^6 + 58*x^5 + 12*x^4 + 77*x^3 + 56*x^2 + 109*x + 82, x^75 + 41*x^73 + 102*x^72 + 18*x^71 + 72*x^70 + 42*x^69 + 68*x^68 + 21*x^67 + 72*x^66 + 85*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 82*x^7 + 72*x^6 + 106*x^5 + 68*x^4 + 61*x^3 + 72*x^2 + 61*x + 102, x^75 + 41*x^73 + 42*x^72 + 18*x^71 + 56*x^70 + 42*x^69 + 92*x^68 + 21*x^67 + 56*x^66 + 85*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 82*x^7 + 56*x^6 + 106*x^5 + 92*x^4 + 61*x^3 + 56*x^2 + 61*x + 106, x^75 + 41*x^73 + 106*x^72 + 114*x^71 + 88*x^70 + 74*x^69 + 60*x^68 + 53*x^67 + 24*x^66 + 53*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 50*x^7 + 88*x^6 + 10*x^5 + 60*x^4 + 93*x^3 + 24*x^2 + 29*x + 74, x^75 + 41*x^73 + 58*x^72 + 114*x^71 + 24*x^70 + 10*x^69 + 92*x^68 + 53*x^67 + 88*x^66 + 117*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 50*x^7 + 24*x^6 + 74*x^5 + 92*x^4 + 93*x^3 + 88*x^2 + 93*x + 90, x^75 + 41*x^73 + 2*x^72 + 66*x^71 + 88*x^70 + 58*x^69 + 12*x^68 + 101*x^67 + 24*x^66 + 69*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 2*x^7 + 88*x^6 + 122*x^5 + 12*x^4 + 13*x^3 + 24*x^2 + 45*x + 98, x^75 + 41*x^73 + 78*x^72 + 18*x^71 + 120*x^70 + 10*x^69 + 36*x^68 + 85*x^67 + 88*x^66 + 53*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 82*x^7 + 120*x^6 + 74*x^5 + 36*x^4 + 125*x^3 + 88*x^2 + 29*x + 94, x^75 + 41*x^73 + 74*x^72 + 2*x^71 + 40*x^70 + 90*x^69 + 12*x^68 + 101*x^67 + 8*x^66 + 101*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 66*x^7 + 40*x^6 + 26*x^5 + 12*x^4 + 13*x^3 + 8*x^2 + 77*x + 90, x^75 + 41*x^73 + 122*x^72 + 114*x^71 + 56*x^70 + 10*x^69 + 124*x^68 + 53*x^67 + 56*x^66 + 117*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 50*x^7 + 56*x^6 + 74*x^5 + 124*x^4 + 93*x^3 + 56*x^2 + 93*x + 122, x^75 + 41*x^73 + 2*x^72 + 18*x^71 + 40*x^70 + 74*x^69 + 92*x^68 + 85*x^67 + 8*x^66 + 117*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 82*x^7 + 40*x^6 + 10*x^5 + 92*x^4 + 125*x^3 + 8*x^2 + 93*x + 82, x^75 + 41*x^73 + 58*x^72 + 18*x^71 + 88*x^70 + 106*x^69 + 92*x^68 + 21*x^67 + 24*x^66 + 21*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 82*x^7 + 88*x^6 + 42*x^5 + 92*x^4 + 61*x^3 + 24*x^2 + 125*x + 90, x^75 + 41*x^73 + 54*x^72 + 98*x^71 + 120*x^70 + 122*x^69 + 84*x^68 + 5*x^67 + 88*x^66 + 69*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 34*x^7 + 120*x^6 + 58*x^5 + 84*x^4 + 45*x^3 + 88*x^2 + 45*x + 70, x^75 + 41*x^73 + 126*x^72 + 82*x^71 + 120*x^70 + 10*x^69 + 68*x^68 + 21*x^67 + 88*x^66 + 53*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 18*x^7 + 120*x^6 + 74*x^5 + 68*x^4 + 61*x^3 + 88*x^2 + 29*x + 14, x^75 + 41*x^73 + 42*x^72 + 66*x^71 + 8*x^70 + 26*x^69 + 44*x^68 + 37*x^67 + 40*x^66 + 37*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 2*x^7 + 8*x^6 + 90*x^5 + 44*x^4 + 77*x^3 + 40*x^2 + 13*x + 90, x^75 + 41*x^73 + 58*x^72 + 2*x^71 + 72*x^70 + 26*x^69 + 76*x^68 + 101*x^67 + 104*x^66 + 37*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 66*x^7 + 72*x^6 + 90*x^5 + 76*x^4 + 13*x^3 + 104*x^2 + 13*x + 42, x^75 + 41*x^73 + 30*x^72 + 2*x^71 + 8*x^70 + 58*x^69 + 84*x^68 + 37*x^67 + 8*x^66 + 69*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 66*x^7 + 8*x^6 + 122*x^5 + 84*x^4 + 77*x^3 + 8*x^2 + 45*x + 30, x^75 + 41*x^73 + 2*x^72 + 34*x^71 + 120*x^70 + 90*x^69 + 108*x^68 + 5*x^67 + 120*x^66 + 37*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 98*x^7 + 120*x^6 + 26*x^5 + 108*x^4 + 45*x^3 + 120*x^2 + 13*x + 2, x^75 + 41*x^73 + 90*x^72 + 50*x^71 + 24*x^70 + 10*x^69 + 92*x^68 + 117*x^67 + 88*x^66 + 117*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 114*x^7 + 24*x^6 + 74*x^5 + 92*x^4 + 29*x^3 + 88*x^2 + 93*x + 58, x^75 + 41*x^73 + 14*x^72 + 82*x^71 + 56*x^70 + 10*x^69 + 36*x^68 + 21*x^67 + 24*x^66 + 53*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 18*x^7 + 56*x^6 + 74*x^5 + 36*x^4 + 61*x^3 + 24*x^2 + 29*x + 30, x^75 + 41*x^73 + 18*x^72 + 98*x^71 + 56*x^70 + 90*x^69 + 12*x^68 + 69*x^67 + 56*x^66 + 37*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 34*x^7 + 56*x^6 + 26*x^5 + 12*x^4 + 109*x^3 + 56*x^2 + 13*x + 82, x^75 + 41*x^73 + 118*x^72 + 82*x^71 + 8*x^70 + 106*x^69 + 36*x^68 + 85*x^67 + 8*x^66 + 21*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 18*x^7 + 8*x^6 + 42*x^5 + 36*x^4 + 125*x^3 + 8*x^2 + 125*x + 118, x^75 + 41*x^73 + 2*x^72 + 66*x^71 + 56*x^70 + 122*x^69 + 44*x^68 + 101*x^67 + 56*x^66 + 5*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 2*x^7 + 56*x^6 + 58*x^5 + 44*x^4 + 13*x^3 + 56*x^2 + 109*x + 66, x^75 + 41*x^73 + 118*x^72 + 98*x^71 + 24*x^70 + 122*x^69 + 116*x^68 + 5*x^67 + 56*x^66 + 69*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 34*x^7 + 24*x^6 + 58*x^5 + 116*x^4 + 45*x^3 + 56*x^2 + 45*x + 102, x^75 + 41*x^73 + 66*x^72 + 18*x^71 + 104*x^70 + 10*x^69 + 92*x^68 + 85*x^67 + 72*x^66 + 53*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 82*x^7 + 104*x^6 + 74*x^5 + 92*x^4 + 125*x^3 + 72*x^2 + 29*x + 18, x^75 + 41*x^73 + 62*x^72 + 34*x^71 + 40*x^70 + 90*x^69 + 52*x^68 + 5*x^67 + 104*x^66 + 37*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 98*x^7 + 40*x^6 + 26*x^5 + 52*x^4 + 45*x^3 + 104*x^2 + 13*x + 30, x^75 + 41*x^73 + 10*x^72 + 18*x^71 + 56*x^70 + 42*x^69 + 28*x^68 + 21*x^67 + 56*x^66 + 85*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 82*x^7 + 56*x^6 + 106*x^5 + 28*x^4 + 61*x^3 + 56*x^2 + 61*x + 74, x^75 + 41*x^73 + 118*x^72 + 2*x^71 + 24*x^70 + 26*x^69 + 116*x^68 + 101*x^67 + 56*x^66 + 37*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 66*x^7 + 24*x^6 + 90*x^5 + 116*x^4 + 13*x^3 + 56*x^2 + 13*x + 102, x^75 + 41*x^73 + 46*x^72 + 66*x^71 + 104*x^70 + 122*x^69 + 84*x^68 + 101*x^67 + 40*x^66 + 5*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 2*x^7 + 104*x^6 + 58*x^5 + 84*x^4 + 13*x^3 + 40*x^2 + 109*x + 14, x^75 + 41*x^73 + 94*x^72 + 34*x^71 + 40*x^70 + 90*x^69 + 116*x^68 + 5*x^67 + 104*x^66 + 37*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 98*x^7 + 40*x^6 + 26*x^5 + 116*x^4 + 45*x^3 + 104*x^2 + 13*x + 62, x^75 + 41*x^73 + 114*x^72 + 50*x^71 + 72*x^70 + 106*x^69 + 92*x^68 + 53*x^67 + 104*x^66 + 85*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 114*x^7 + 72*x^6 + 42*x^5 + 92*x^4 + 93*x^3 + 104*x^2 + 61*x + 98, x^75 + 41*x^73 + 94*x^72 + 82*x^71 + 24*x^70 + 10*x^69 + 36*x^68 + 21*x^67 + 56*x^66 + 53*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 18*x^7 + 24*x^6 + 74*x^5 + 36*x^4 + 61*x^3 + 56*x^2 + 29*x + 78, x^75 + 41*x^73 + 10*x^72 + 2*x^71 + 104*x^70 + 26*x^69 + 12*x^68 + 101*x^67 + 72*x^66 + 37*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 66*x^7 + 104*x^6 + 90*x^5 + 12*x^4 + 13*x^3 + 72*x^2 + 13*x + 26, x^75 + 41*x^73 + 90*x^72 + 18*x^71 + 120*x^70 + 42*x^69 + 124*x^68 + 21*x^67 + 120*x^66 + 85*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 82*x^7 + 120*x^6 + 106*x^5 + 124*x^4 + 61*x^3 + 120*x^2 + 61*x + 26, x^75 + 41*x^73 + 50*x^72 + 50*x^71 + 8*x^70 + 42*x^69 + 92*x^68 + 53*x^67 + 40*x^66 + 21*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 114*x^7 + 8*x^6 + 106*x^5 + 92*x^4 + 93*x^3 + 40*x^2 + 125*x + 34, x^75 + 41*x^73 + 38*x^72 + 2*x^71 + 88*x^70 + 26*x^69 + 20*x^68 + 101*x^67 + 120*x^66 + 37*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 66*x^7 + 88*x^6 + 90*x^5 + 20*x^4 + 13*x^3 + 120*x^2 + 13*x + 22, x^75 + 41*x^73 + 114*x^72 + 66*x^71 + 56*x^70 + 58*x^69 + 76*x^68 + 101*x^67 + 56*x^66 + 69*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 2*x^7 + 56*x^6 + 122*x^5 + 76*x^4 + 13*x^3 + 56*x^2 + 45*x + 50, x^75 + 41*x^73 + 102*x^72 + 50*x^71 + 40*x^70 + 74*x^69 + 36*x^68 + 117*x^67 + 104*x^66 + 53*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 114*x^7 + 40*x^6 + 10*x^5 + 36*x^4 + 29*x^3 + 104*x^2 + 29*x + 6, x^75 + 41*x^73 + 114*x^72 + 98*x^71 + 88*x^70 + 90*x^69 + 108*x^68 + 69*x^67 + 24*x^66 + 37*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 34*x^7 + 88*x^6 + 26*x^5 + 108*x^4 + 109*x^3 + 24*x^2 + 13*x + 18, x^75 + 41*x^73 + 46*x^72 + 34*x^71 + 8*x^70 + 26*x^69 + 52*x^68 + 5*x^67 + 8*x^66 + 101*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 98*x^7 + 8*x^6 + 90*x^5 + 52*x^4 + 45*x^3 + 8*x^2 + 77*x + 46, x^75 + 41*x^73 + 70*x^72 + 114*x^71 + 72*x^70 + 10*x^69 + 4*x^68 + 53*x^67 + 72*x^66 + 117*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 50*x^7 + 72*x^6 + 74*x^5 + 4*x^4 + 93*x^3 + 72*x^2 + 93*x + 70, x^75 + 41*x^73 + 58*x^72 + 18*x^71 + 56*x^70 + 106*x^69 + 60*x^68 + 21*x^67 + 56*x^66 + 21*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 82*x^7 + 56*x^6 + 42*x^5 + 60*x^4 + 61*x^3 + 56*x^2 + 125*x + 122, x^75 + 41*x^73 + 70*x^72 + 114*x^71 + 72*x^70 + 74*x^69 + 68*x^68 + 53*x^67 + 72*x^66 + 53*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 50*x^7 + 72*x^6 + 10*x^5 + 68*x^4 + 93*x^3 + 72*x^2 + 29*x + 6, x^75 + 41*x^73 + 74*x^72 + 34*x^71 + 104*x^70 + 122*x^69 + 76*x^68 + 69*x^67 + 72*x^66 + 69*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 98*x^7 + 104*x^6 + 58*x^5 + 76*x^4 + 109*x^3 + 72*x^2 + 45*x + 26, x^75 + 41*x^73 + 14*x^72 + 82*x^71 + 56*x^70 + 74*x^69 + 100*x^68 + 21*x^67 + 24*x^66 + 117*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 18*x^7 + 56*x^6 + 10*x^5 + 100*x^4 + 61*x^3 + 24*x^2 + 93*x + 94, x^75 + 41*x^73 + 18*x^72 + 66*x^71 + 24*x^70 + 122*x^69 + 44*x^68 + 101*x^67 + 88*x^66 + 5*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 2*x^7 + 24*x^6 + 58*x^5 + 44*x^4 + 13*x^3 + 88*x^2 + 109*x + 50, x^75 + 41*x^73 + 34*x^72 + 66*x^71 + 56*x^70 + 58*x^69 + 44*x^68 + 101*x^67 + 56*x^66 + 69*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 2*x^7 + 56*x^6 + 122*x^5 + 44*x^4 + 13*x^3 + 56*x^2 + 45*x + 34, x^75 + 41*x^73 + 70*x^72 + 66*x^71 + 56*x^70 + 26*x^69 + 116*x^68 + 37*x^67 + 24*x^66 + 37*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 2*x^7 + 56*x^6 + 90*x^5 + 116*x^4 + 77*x^3 + 24*x^2 + 13*x + 22, x^75 + 41*x^73 + 26*x^72 + 114*x^71 + 120*x^70 + 10*x^69 + 124*x^68 + 53*x^67 + 120*x^66 + 117*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 50*x^7 + 120*x^6 + 74*x^5 + 124*x^4 + 93*x^3 + 120*x^2 + 93*x + 90, x^75 + 41*x^73 + 50*x^72 + 34*x^71 + 24*x^70 + 90*x^69 + 108*x^68 + 5*x^67 + 88*x^66 + 37*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 98*x^7 + 24*x^6 + 26*x^5 + 108*x^4 + 45*x^3 + 88*x^2 + 13*x + 82, x^75 + 41*x^73 + 74*x^72 + 34*x^71 + 72*x^70 + 58*x^69 + 108*x^68 + 69*x^67 + 104*x^66 + 5*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 98*x^7 + 72*x^6 + 122*x^5 + 108*x^4 + 109*x^3 + 104*x^2 + 109*x + 122, x^75 + 41*x^73 + 10*x^72 + 50*x^71 + 24*x^70 + 10*x^69 + 60*x^68 + 117*x^67 + 88*x^66 + 117*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 114*x^7 + 24*x^6 + 74*x^5 + 60*x^4 + 29*x^3 + 88*x^2 + 93*x + 42, x^75 + 41*x^73 + 22*x^72 + 66*x^71 + 56*x^70 + 90*x^69 + 84*x^68 + 37*x^67 + 24*x^66 + 101*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 2*x^7 + 56*x^6 + 26*x^5 + 84*x^4 + 77*x^3 + 24*x^2 + 77*x + 102, x^75 + 41*x^73 + 46*x^72 + 50*x^71 + 24*x^70 + 106*x^69 + 68*x^68 + 53*x^67 + 56*x^66 + 85*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 114*x^7 + 24*x^6 + 42*x^5 + 68*x^4 + 93*x^3 + 56*x^2 + 61*x + 94, x^75 + 41*x^73 + 78*x^72 + 98*x^71 + 72*x^70 + 90*x^69 + 52*x^68 + 69*x^67 + 72*x^66 + 37*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 34*x^7 + 72*x^6 + 26*x^5 + 52*x^4 + 109*x^3 + 72*x^2 + 13*x + 14, x^75 + 41*x^73 + 2*x^72 + 98*x^71 + 24*x^70 + 26*x^69 + 12*x^68 + 69*x^67 + 88*x^66 + 101*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 34*x^7 + 24*x^6 + 90*x^5 + 12*x^4 + 109*x^3 + 88*x^2 + 77*x + 98, x^75 + 41*x^73 + 82*x^72 + 114*x^71 + 72*x^70 + 106*x^69 + 92*x^68 + 117*x^67 + 104*x^66 + 85*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 50*x^7 + 72*x^6 + 42*x^5 + 92*x^4 + 29*x^3 + 104*x^2 + 61*x + 2, x^75 + 41*x^73 + 34*x^72 + 98*x^71 + 56*x^70 + 26*x^69 + 108*x^68 + 69*x^67 + 56*x^66 + 101*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 34*x^7 + 56*x^6 + 90*x^5 + 108*x^4 + 109*x^3 + 56*x^2 + 77*x + 98, x^75 + 41*x^73 + 54*x^72 + 82*x^71 + 72*x^70 + 42*x^69 + 36*x^68 + 85*x^67 + 72*x^66 + 85*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 18*x^7 + 72*x^6 + 106*x^5 + 36*x^4 + 125*x^3 + 72*x^2 + 61*x + 54, x^75 + 41*x^73 + 46*x^72 + 82*x^71 + 24*x^70 + 74*x^69 + 4*x^68 + 21*x^67 + 56*x^66 + 117*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 18*x^7 + 24*x^6 + 10*x^5 + 4*x^4 + 61*x^3 + 56*x^2 + 93*x + 30, x^75 + 41*x^73 + 6*x^72 + 2*x^71 + 120*x^70 + 90*x^69 + 52*x^68 + 101*x^67 + 88*x^66 + 101*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 66*x^7 + 120*x^6 + 26*x^5 + 52*x^4 + 13*x^3 + 88*x^2 + 77*x + 22, x^75 + 41*x^73 + 94*x^72 + 82*x^71 + 56*x^70 + 10*x^69 + 68*x^68 + 21*x^67 + 24*x^66 + 53*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 18*x^7 + 56*x^6 + 74*x^5 + 68*x^4 + 61*x^3 + 24*x^2 + 29*x + 46, x^75 + 41*x^73 + 42*x^72 + 2*x^71 + 72*x^70 + 26*x^69 + 44*x^68 + 101*x^67 + 104*x^66 + 37*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 66*x^7 + 72*x^6 + 90*x^5 + 44*x^4 + 13*x^3 + 104*x^2 + 13*x + 90, x^75 + 41*x^73 + 2*x^72 + 66*x^71 + 24*x^70 + 58*x^69 + 76*x^68 + 101*x^67 + 88*x^66 + 69*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 2*x^7 + 24*x^6 + 122*x^5 + 76*x^4 + 13*x^3 + 88*x^2 + 45*x + 34, x^75 + 41*x^73 + 114*x^72 + 2*x^71 + 24*x^70 + 122*x^69 + 44*x^68 + 37*x^67 + 88*x^66 + 5*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 66*x^7 + 24*x^6 + 58*x^5 + 44*x^4 + 77*x^3 + 88*x^2 + 109*x + 82, x^75 + 41*x^73 + 50*x^72 + 66*x^71 + 56*x^70 + 58*x^69 + 76*x^68 + 101*x^67 + 56*x^66 + 69*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 2*x^7 + 56*x^6 + 122*x^5 + 76*x^4 + 13*x^3 + 56*x^2 + 45*x + 114, x^75 + 41*x^73 + 118*x^72 + 34*x^71 + 88*x^70 + 122*x^69 + 116*x^68 + 69*x^67 + 120*x^66 + 69*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 98*x^7 + 88*x^6 + 58*x^5 + 116*x^4 + 109*x^3 + 120*x^2 + 45*x + 102, x^75 + 41*x^73 + 106*x^72 + 2*x^71 + 72*x^70 + 26*x^69 + 44*x^68 + 101*x^67 + 104*x^66 + 37*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 66*x^7 + 72*x^6 + 90*x^5 + 44*x^4 + 13*x^3 + 104*x^2 + 13*x + 26, x^75 + 41*x^73 + 102*x^72 + 18*x^71 + 104*x^70 + 42*x^69 + 100*x^68 + 21*x^67 + 40*x^66 + 85*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 82*x^7 + 104*x^6 + 106*x^5 + 100*x^4 + 61*x^3 + 40*x^2 + 61*x + 70, x^75 + 41*x^73 + 26*x^72 + 114*x^71 + 56*x^70 + 74*x^69 + 124*x^68 + 53*x^67 + 56*x^66 + 53*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 50*x^7 + 56*x^6 + 10*x^5 + 124*x^4 + 93*x^3 + 56*x^2 + 29*x + 90, x^75 + 41*x^73 + 102*x^72 + 50*x^71 + 72*x^70 + 74*x^69 + 68*x^68 + 117*x^67 + 72*x^66 + 53*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 114*x^7 + 72*x^6 + 10*x^5 + 68*x^4 + 29*x^3 + 72*x^2 + 29*x + 102, x^75 + 41*x^73 + 14*x^72 + 114*x^71 + 56*x^70 + 106*x^69 + 100*x^68 + 117*x^67 + 24*x^66 + 85*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 50*x^7 + 56*x^6 + 42*x^5 + 100*x^4 + 29*x^3 + 24*x^2 + 61*x + 94, x^75 + 41*x^73 + 82*x^72 + 18*x^71 + 72*x^70 + 74*x^69 + 28*x^68 + 85*x^67 + 104*x^66 + 117*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 82*x^7 + 72*x^6 + 10*x^5 + 28*x^4 + 125*x^3 + 104*x^2 + 93*x + 66, x^75 + 41*x^73 + 46*x^72 + 114*x^71 + 88*x^70 + 42*x^69 + 4*x^68 + 117*x^67 + 120*x^66 + 21*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 50*x^7 + 88*x^6 + 106*x^5 + 4*x^4 + 29*x^3 + 120*x^2 + 125*x + 30, x^75 + 41*x^73 + 34*x^72 + 34*x^71 + 24*x^70 + 26*x^69 + 12*x^68 + 5*x^67 + 88*x^66 + 101*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 98*x^7 + 24*x^6 + 90*x^5 + 12*x^4 + 45*x^3 + 88*x^2 + 77*x + 66, x^75 + 41*x^73 + 122*x^72 + 50*x^71 + 120*x^70 + 74*x^69 + 60*x^68 + 117*x^67 + 120*x^66 + 53*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 114*x^7 + 120*x^6 + 10*x^5 + 60*x^4 + 29*x^3 + 120*x^2 + 29*x + 58, x^75 + 41*x^73 + 26*x^72 + 2*x^71 + 104*x^70 + 90*x^69 + 108*x^68 + 101*x^67 + 72*x^66 + 101*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 66*x^7 + 104*x^6 + 26*x^5 + 108*x^4 + 13*x^3 + 72*x^2 + 77*x + 42, x^75 + 41*x^73 + 126*x^72 + 2*x^71 + 72*x^70 + 58*x^69 + 84*x^68 + 37*x^67 + 72*x^66 + 69*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 66*x^7 + 72*x^6 + 122*x^5 + 84*x^4 + 77*x^3 + 72*x^2 + 45*x + 62, x^75 + 41*x^73 + 26*x^72 + 82*x^71 + 56*x^70 + 42*x^69 + 124*x^68 + 85*x^67 + 56*x^66 + 85*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 18*x^7 + 56*x^6 + 106*x^5 + 124*x^4 + 125*x^3 + 56*x^2 + 61*x + 90, x^75 + 41*x^73 + 114*x^72 + 2*x^71 + 88*x^70 + 58*x^69 + 44*x^68 + 37*x^67 + 24*x^66 + 69*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 66*x^7 + 88*x^6 + 122*x^5 + 44*x^4 + 77*x^3 + 24*x^2 + 45*x + 82, x^75 + 41*x^73 + 82*x^72 + 98*x^71 + 120*x^70 + 90*x^69 + 76*x^68 + 69*x^67 + 120*x^66 + 37*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 34*x^7 + 120*x^6 + 26*x^5 + 76*x^4 + 109*x^3 + 120*x^2 + 13*x + 82, x^75 + 41*x^73 + 18*x^72 + 50*x^71 + 72*x^70 + 106*x^69 + 28*x^68 + 53*x^67 + 104*x^66 + 85*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 114*x^7 + 72*x^6 + 42*x^5 + 28*x^4 + 93*x^3 + 104*x^2 + 61*x + 2, x^75 + 41*x^73 + 122*x^72 + 2*x^71 + 40*x^70 + 90*x^69 + 108*x^68 + 101*x^67 + 8*x^66 + 101*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 66*x^7 + 40*x^6 + 26*x^5 + 108*x^4 + 13*x^3 + 8*x^2 + 77*x + 74, x^75 + 41*x^73 + 106*x^72 + 82*x^71 + 24*x^70 + 42*x^69 + 124*x^68 + 85*x^67 + 88*x^66 + 85*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 18*x^7 + 24*x^6 + 106*x^5 + 124*x^4 + 125*x^3 + 88*x^2 + 61*x + 10, x^75 + 41*x^73 + 122*x^72 + 98*x^71 + 104*x^70 + 58*x^69 + 44*x^68 + 5*x^67 + 72*x^66 + 5*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 34*x^7 + 104*x^6 + 122*x^5 + 44*x^4 + 45*x^3 + 72*x^2 + 109*x + 10, x^75 + 41*x^73 + 34*x^72 + 18*x^71 + 40*x^70 + 10*x^69 + 92*x^68 + 85*x^67 + 8*x^66 + 53*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 82*x^7 + 40*x^6 + 74*x^5 + 92*x^4 + 125*x^3 + 8*x^2 + 29*x + 50, x^75 + 41*x^73 + 98*x^72 + 50*x^71 + 40*x^70 + 42*x^69 + 92*x^68 + 53*x^67 + 8*x^66 + 21*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 114*x^7 + 40*x^6 + 106*x^5 + 92*x^4 + 93*x^3 + 8*x^2 + 125*x + 114, x^75 + 41*x^73 + 82*x^72 + 66*x^71 + 24*x^70 + 58*x^69 + 108*x^68 + 101*x^67 + 88*x^66 + 69*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 2*x^7 + 24*x^6 + 122*x^5 + 108*x^4 + 13*x^3 + 88*x^2 + 45*x + 50, x^75 + 41*x^73 + 10*x^72 + 66*x^71 + 40*x^70 + 90*x^69 + 76*x^68 + 37*x^67 + 8*x^66 + 101*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 2*x^7 + 40*x^6 + 26*x^5 + 76*x^4 + 77*x^3 + 8*x^2 + 77*x + 90, x^75 + 41*x^73 + 74*x^72 + 114*x^71 + 56*x^70 + 74*x^69 + 92*x^68 + 53*x^67 + 56*x^66 + 53*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 50*x^7 + 56*x^6 + 10*x^5 + 92*x^4 + 93*x^3 + 56*x^2 + 29*x + 74, x^75 + 41*x^73 + 58*x^72 + 18*x^71 + 24*x^70 + 42*x^69 + 92*x^68 + 21*x^67 + 88*x^66 + 85*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 82*x^7 + 24*x^6 + 106*x^5 + 92*x^4 + 61*x^3 + 88*x^2 + 61*x + 90, x^75 + 41*x^73 + 54*x^72 + 82*x^71 + 40*x^70 + 42*x^69 + 4*x^68 + 85*x^67 + 104*x^66 + 85*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 18*x^7 + 40*x^6 + 106*x^5 + 4*x^4 + 125*x^3 + 104*x^2 + 61*x + 86, x^75 + 41*x^73 + 98*x^72 + 82*x^71 + 40*x^70 + 10*x^69 + 28*x^68 + 21*x^67 + 8*x^66 + 53*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 18*x^7 + 40*x^6 + 74*x^5 + 28*x^4 + 61*x^3 + 8*x^2 + 29*x + 50, x^75 + 41*x^73 + 118*x^72 + 66*x^71 + 120*x^70 + 26*x^69 + 20*x^68 + 37*x^67 + 88*x^66 + 37*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 2*x^7 + 120*x^6 + 90*x^5 + 20*x^4 + 77*x^3 + 88*x^2 + 13*x + 70, x^75 + 41*x^73 + 98*x^72 + 98*x^71 + 24*x^70 + 26*x^69 + 76*x^68 + 69*x^67 + 88*x^66 + 101*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 34*x^7 + 24*x^6 + 90*x^5 + 76*x^4 + 109*x^3 + 88*x^2 + 77*x + 66, x^75 + 41*x^73 + 82*x^72 + 98*x^71 + 56*x^70 + 26*x^69 + 76*x^68 + 69*x^67 + 56*x^66 + 101*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 34*x^7 + 56*x^6 + 90*x^5 + 76*x^4 + 109*x^3 + 56*x^2 + 77*x + 82, x^75 + 41*x^73 + 70*x^72 + 2*x^71 + 56*x^70 + 90*x^69 + 116*x^68 + 101*x^67 + 24*x^66 + 101*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 66*x^7 + 56*x^6 + 26*x^5 + 116*x^4 + 13*x^3 + 24*x^2 + 77*x + 22, x^75 + 41*x^73 + 118*x^72 + 2*x^71 + 120*x^70 + 26*x^69 + 84*x^68 + 101*x^67 + 88*x^66 + 37*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 66*x^7 + 120*x^6 + 90*x^5 + 84*x^4 + 13*x^3 + 88*x^2 + 13*x + 6, x^75 + 41*x^73 + 122*x^72 + 18*x^71 + 56*x^70 + 42*x^69 + 124*x^68 + 21*x^67 + 56*x^66 + 85*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 82*x^7 + 56*x^6 + 106*x^5 + 124*x^4 + 61*x^3 + 56*x^2 + 61*x + 122, x^75 + 41*x^73 + 38*x^72 + 34*x^71 + 120*x^70 + 58*x^69 + 52*x^68 + 69*x^67 + 88*x^66 + 5*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 98*x^7 + 120*x^6 + 122*x^5 + 52*x^4 + 109*x^3 + 88*x^2 + 109*x + 118, x^75 + 41*x^73 + 38*x^72 + 66*x^71 + 24*x^70 + 90*x^69 + 84*x^68 + 37*x^67 + 56*x^66 + 101*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 2*x^7 + 24*x^6 + 26*x^5 + 84*x^4 + 77*x^3 + 56*x^2 + 77*x + 86, x^75 + 41*x^73 + 14*x^72 + 82*x^71 + 120*x^70 + 74*x^69 + 36*x^68 + 21*x^67 + 88*x^66 + 117*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 18*x^7 + 120*x^6 + 10*x^5 + 36*x^4 + 61*x^3 + 88*x^2 + 93*x + 30, x^75 + 41*x^73 + 98*x^72 + 50*x^71 + 8*x^70 + 42*x^69 + 60*x^68 + 53*x^67 + 40*x^66 + 21*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 114*x^7 + 8*x^6 + 106*x^5 + 60*x^4 + 93*x^3 + 40*x^2 + 125*x + 18, x^75 + 41*x^73 + 14*x^72 + 50*x^71 + 88*x^70 + 106*x^69 + 68*x^68 + 53*x^67 + 120*x^66 + 85*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 114*x^7 + 88*x^6 + 42*x^5 + 68*x^4 + 93*x^3 + 120*x^2 + 61*x + 126, x^75 + 41*x^73 + 46*x^72 + 82*x^71 + 120*x^70 + 10*x^69 + 36*x^68 + 21*x^67 + 88*x^66 + 53*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 18*x^7 + 120*x^6 + 74*x^5 + 36*x^4 + 61*x^3 + 88*x^2 + 29*x + 126, x^75 + 41*x^73 + 98*x^72 + 66*x^71 + 120*x^70 + 58*x^69 + 108*x^68 + 101*x^67 + 120*x^66 + 69*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 2*x^7 + 120*x^6 + 122*x^5 + 108*x^4 + 13*x^3 + 120*x^2 + 45*x + 34, x^75 + 41*x^73 + 90*x^72 + 18*x^71 + 24*x^70 + 106*x^69 + 92*x^68 + 21*x^67 + 88*x^66 + 21*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 82*x^7 + 24*x^6 + 42*x^5 + 92*x^4 + 61*x^3 + 88*x^2 + 125*x + 58, x^75 + 41*x^73 + 62*x^72 + 114*x^71 + 24*x^70 + 106*x^69 + 36*x^68 + 117*x^67 + 56*x^66 + 85*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 50*x^7 + 24*x^6 + 42*x^5 + 36*x^4 + 29*x^3 + 56*x^2 + 61*x + 110, x^75 + 41*x^73 + 38*x^72 + 114*x^71 + 40*x^70 + 74*x^69 + 100*x^68 + 53*x^67 + 104*x^66 + 53*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 50*x^7 + 40*x^6 + 10*x^5 + 100*x^4 + 93*x^3 + 104*x^2 + 29*x + 6, x^75 + 41*x^73 + 2*x^72 + 18*x^71 + 40*x^70 + 10*x^69 + 28*x^68 + 85*x^67 + 8*x^66 + 53*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 82*x^7 + 40*x^6 + 74*x^5 + 28*x^4 + 125*x^3 + 8*x^2 + 29*x + 18, x^75 + 41*x^73 + 50*x^72 + 66*x^71 + 120*x^70 + 58*x^69 + 12*x^68 + 101*x^67 + 120*x^66 + 69*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 2*x^7 + 120*x^6 + 122*x^5 + 12*x^4 + 13*x^3 + 120*x^2 + 45*x + 50, x^75 + 41*x^73 + 66*x^72 + 2*x^71 + 24*x^70 + 58*x^69 + 12*x^68 + 37*x^67 + 88*x^66 + 69*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 66*x^7 + 24*x^6 + 122*x^5 + 12*x^4 + 77*x^3 + 88*x^2 + 45*x + 34, x^75 + 41*x^73 + 90*x^72 + 50*x^71 + 120*x^70 + 74*x^69 + 124*x^68 + 117*x^67 + 120*x^66 + 53*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 114*x^7 + 120*x^6 + 10*x^5 + 124*x^4 + 29*x^3 + 120*x^2 + 29*x + 26, x^75 + 41*x^73 + 6*x^72 + 50*x^71 + 72*x^70 + 74*x^69 + 4*x^68 + 117*x^67 + 72*x^66 + 53*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 114*x^7 + 72*x^6 + 10*x^5 + 4*x^4 + 29*x^3 + 72*x^2 + 29*x + 6, x^75 + 41*x^73 + 6*x^72 + 114*x^71 + 40*x^70 + 74*x^69 + 36*x^68 + 53*x^67 + 104*x^66 + 53*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 50*x^7 + 40*x^6 + 10*x^5 + 36*x^4 + 93*x^3 + 104*x^2 + 29*x + 102, x^75 + 41*x^73 + 18*x^72 + 66*x^71 + 88*x^70 + 58*x^69 + 44*x^68 + 101*x^67 + 24*x^66 + 69*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 2*x^7 + 88*x^6 + 122*x^5 + 44*x^4 + 13*x^3 + 24*x^2 + 45*x + 50, x^75 + 41*x^73 + 114*x^72 + 114*x^71 + 8*x^70 + 106*x^69 + 92*x^68 + 117*x^67 + 40*x^66 + 85*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 50*x^7 + 8*x^6 + 42*x^5 + 92*x^4 + 29*x^3 + 40*x^2 + 61*x + 98, x^75 + 41*x^73 + 26*x^72 + 34*x^71 + 104*x^70 + 58*x^69 + 44*x^68 + 69*x^67 + 72*x^66 + 5*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 98*x^7 + 104*x^6 + 122*x^5 + 44*x^4 + 109*x^3 + 72*x^2 + 109*x + 106, x^75 + 41*x^73 + 86*x^72 + 82*x^71 + 72*x^70 + 42*x^69 + 100*x^68 + 85*x^67 + 72*x^66 + 85*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 18*x^7 + 72*x^6 + 106*x^5 + 100*x^4 + 125*x^3 + 72*x^2 + 61*x + 86, x^75 + 41*x^73 + 98*x^72 + 82*x^71 + 104*x^70 + 74*x^69 + 28*x^68 + 21*x^67 + 72*x^66 + 117*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 18*x^7 + 104*x^6 + 10*x^5 + 28*x^4 + 61*x^3 + 72*x^2 + 93*x + 50, x^75 + 41*x^73 + 46*x^72 + 34*x^71 + 72*x^70 + 26*x^69 + 116*x^68 + 5*x^67 + 72*x^66 + 101*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 98*x^7 + 72*x^6 + 90*x^5 + 116*x^4 + 45*x^3 + 72*x^2 + 77*x + 110, x^75 + 41*x^73 + 38*x^72 + 98*x^71 + 56*x^70 + 58*x^69 + 52*x^68 + 5*x^67 + 24*x^66 + 5*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 34*x^7 + 56*x^6 + 122*x^5 + 52*x^4 + 45*x^3 + 24*x^2 + 109*x + 118, x^75 + 41*x^73 + 42*x^72 + 114*x^71 + 120*x^70 + 74*x^69 + 92*x^68 + 53*x^67 + 120*x^66 + 53*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 50*x^7 + 120*x^6 + 10*x^5 + 92*x^4 + 93*x^3 + 120*x^2 + 29*x + 106, x^75 + 41*x^73 + 82*x^72 + 82*x^71 + 40*x^70 + 74*x^69 + 60*x^68 + 21*x^67 + 8*x^66 + 117*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 18*x^7 + 40*x^6 + 10*x^5 + 60*x^4 + 61*x^3 + 8*x^2 + 93*x + 34, x^75 + 41*x^73 + 30*x^72 + 18*x^71 + 88*x^70 + 74*x^69 + 100*x^68 + 85*x^67 + 120*x^66 + 117*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 82*x^7 + 88*x^6 + 10*x^5 + 100*x^4 + 125*x^3 + 120*x^2 + 93*x + 78, x^75 + 41*x^73 + 2*x^72 + 82*x^71 + 8*x^70 + 10*x^69 + 60*x^68 + 21*x^67 + 40*x^66 + 53*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 18*x^7 + 8*x^6 + 74*x^5 + 60*x^4 + 61*x^3 + 40*x^2 + 29*x + 114, x^75 + 41*x^73 + 70*x^72 + 50*x^71 + 104*x^70 + 74*x^69 + 36*x^68 + 117*x^67 + 40*x^66 + 53*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 114*x^7 + 104*x^6 + 10*x^5 + 36*x^4 + 29*x^3 + 40*x^2 + 29*x + 38, x^75 + 41*x^73 + 42*x^72 + 66*x^71 + 72*x^70 + 90*x^69 + 44*x^68 + 37*x^67 + 104*x^66 + 101*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 2*x^7 + 72*x^6 + 26*x^5 + 44*x^4 + 77*x^3 + 104*x^2 + 77*x + 90, x^75 + 41*x^73 + 38*x^72 + 66*x^71 + 56*x^70 + 26*x^69 + 52*x^68 + 37*x^67 + 24*x^66 + 37*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 2*x^7 + 56*x^6 + 90*x^5 + 52*x^4 + 77*x^3 + 24*x^2 + 13*x + 118, x^75 + 41*x^73 + 42*x^72 + 18*x^71 + 120*x^70 + 42*x^69 + 28*x^68 + 21*x^67 + 120*x^66 + 85*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 82*x^7 + 120*x^6 + 106*x^5 + 28*x^4 + 61*x^3 + 120*x^2 + 61*x + 42, x^75 + 41*x^73 + 110*x^72 + 34*x^71 + 104*x^70 + 26*x^69 + 20*x^68 + 5*x^67 + 40*x^66 + 101*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 98*x^7 + 104*x^6 + 90*x^5 + 20*x^4 + 45*x^3 + 40*x^2 + 77*x + 14, x^75 + 41*x^73 + 34*x^72 + 98*x^71 + 24*x^70 + 26*x^69 + 76*x^68 + 69*x^67 + 88*x^66 + 101*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 34*x^7 + 24*x^6 + 90*x^5 + 76*x^4 + 109*x^3 + 88*x^2 + 77*x + 2, x^75 + 41*x^73 + 46*x^72 + 114*x^71 + 24*x^70 + 106*x^69 + 4*x^68 + 117*x^67 + 56*x^66 + 85*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 50*x^7 + 24*x^6 + 42*x^5 + 4*x^4 + 29*x^3 + 56*x^2 + 61*x + 30, x^75 + 41*x^73 + 74*x^72 + 2*x^71 + 8*x^70 + 26*x^69 + 44*x^68 + 101*x^67 + 40*x^66 + 37*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 66*x^7 + 8*x^6 + 90*x^5 + 44*x^4 + 13*x^3 + 40*x^2 + 13*x + 58, x^75 + 41*x^73 + 110*x^72 + 34*x^71 + 8*x^70 + 90*x^69 + 116*x^68 + 5*x^67 + 8*x^66 + 37*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 98*x^7 + 8*x^6 + 26*x^5 + 116*x^4 + 45*x^3 + 8*x^2 + 13*x + 46, x^75 + 41*x^73 + 2*x^72 + 50*x^71 + 104*x^70 + 106*x^69 + 28*x^68 + 53*x^67 + 72*x^66 + 85*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 114*x^7 + 104*x^6 + 42*x^5 + 28*x^4 + 93*x^3 + 72*x^2 + 61*x + 18, x^75 + 41*x^73 + 22*x^72 + 98*x^71 + 120*x^70 + 58*x^69 + 84*x^68 + 5*x^67 + 88*x^66 + 5*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 34*x^7 + 120*x^6 + 122*x^5 + 84*x^4 + 45*x^3 + 88*x^2 + 109*x + 102, x^75 + 41*x^73 + 54*x^72 + 66*x^71 + 88*x^70 + 26*x^69 + 116*x^68 + 37*x^67 + 120*x^66 + 37*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 2*x^7 + 88*x^6 + 90*x^5 + 116*x^4 + 77*x^3 + 120*x^2 + 13*x + 38, x^75 + 41*x^73 + 26*x^72 + 114*x^71 + 56*x^70 + 10*x^69 + 60*x^68 + 53*x^67 + 56*x^66 + 117*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 50*x^7 + 56*x^6 + 74*x^5 + 60*x^4 + 93*x^3 + 56*x^2 + 93*x + 26, x^75 + 41*x^73 + 26*x^72 + 18*x^71 + 120*x^70 + 42*x^69 + 124*x^68 + 21*x^67 + 120*x^66 + 85*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 82*x^7 + 120*x^6 + 106*x^5 + 124*x^4 + 61*x^3 + 120*x^2 + 61*x + 90, x^75 + 41*x^73 + 114*x^72 + 50*x^71 + 8*x^70 + 42*x^69 + 92*x^68 + 53*x^67 + 40*x^66 + 21*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 114*x^7 + 8*x^6 + 106*x^5 + 92*x^4 + 93*x^3 + 40*x^2 + 125*x + 98, x^75 + 41*x^73 + 54*x^72 + 66*x^71 + 120*x^70 + 26*x^69 + 20*x^68 + 37*x^67 + 88*x^66 + 37*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 2*x^7 + 120*x^6 + 90*x^5 + 20*x^4 + 77*x^3 + 88*x^2 + 13*x + 6, x^75 + 41*x^73 + 106*x^72 + 66*x^71 + 40*x^70 + 26*x^69 + 76*x^68 + 37*x^67 + 8*x^66 + 37*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 2*x^7 + 40*x^6 + 90*x^5 + 76*x^4 + 77*x^3 + 8*x^2 + 13*x + 122, x^75 + 41*x^73 + 18*x^72 + 82*x^71 + 40*x^70 + 74*x^69 + 60*x^68 + 21*x^67 + 8*x^66 + 117*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 18*x^7 + 40*x^6 + 10*x^5 + 60*x^4 + 61*x^3 + 8*x^2 + 93*x + 98, x^75 + 41*x^73 + 18*x^72 + 2*x^71 + 56*x^70 + 58*x^69 + 76*x^68 + 37*x^67 + 56*x^66 + 69*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 66*x^7 + 56*x^6 + 122*x^5 + 76*x^4 + 77*x^3 + 56*x^2 + 45*x + 18, x^75 + 41*x^73 + 62*x^72 + 82*x^71 + 56*x^70 + 10*x^69 + 4*x^68 + 21*x^67 + 24*x^66 + 53*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 18*x^7 + 56*x^6 + 74*x^5 + 4*x^4 + 61*x^3 + 24*x^2 + 29*x + 14, x^75 + 41*x^73 + 6*x^72 + 66*x^71 + 88*x^70 + 26*x^69 + 20*x^68 + 37*x^67 + 120*x^66 + 37*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 2*x^7 + 88*x^6 + 90*x^5 + 20*x^4 + 77*x^3 + 120*x^2 + 13*x + 54, x^75 + 41*x^73 + 126*x^72 + 114*x^71 + 24*x^70 + 106*x^69 + 36*x^68 + 117*x^67 + 56*x^66 + 85*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 50*x^7 + 24*x^6 + 42*x^5 + 36*x^4 + 29*x^3 + 56*x^2 + 61*x + 46, x^75 + 41*x^73 + 14*x^72 + 66*x^71 + 8*x^70 + 58*x^69 + 116*x^68 + 101*x^67 + 8*x^66 + 69*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 2*x^7 + 8*x^6 + 122*x^5 + 116*x^4 + 13*x^3 + 8*x^2 + 45*x + 14, x^75 + 41*x^73 + 90*x^72 + 114*x^71 + 24*x^70 + 74*x^69 + 92*x^68 + 53*x^67 + 88*x^66 + 53*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 50*x^7 + 24*x^6 + 10*x^5 + 92*x^4 + 93*x^3 + 88*x^2 + 29*x + 58, x^75 + 41*x^73 + 2*x^72 + 114*x^71 + 72*x^70 + 42*x^69 + 124*x^68 + 117*x^67 + 104*x^66 + 21*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 50*x^7 + 72*x^6 + 106*x^5 + 124*x^4 + 29*x^3 + 104*x^2 + 125*x + 50, x^75 + 41*x^73 + 102*x^72 + 98*x^71 + 24*x^70 + 58*x^69 + 20*x^68 + 5*x^67 + 56*x^66 + 5*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 34*x^7 + 24*x^6 + 122*x^5 + 20*x^4 + 45*x^3 + 56*x^2 + 109*x + 86, x^75 + 41*x^73 + 58*x^72 + 98*x^71 + 72*x^70 + 58*x^69 + 12*x^68 + 5*x^67 + 104*x^66 + 5*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 34*x^7 + 72*x^6 + 122*x^5 + 12*x^4 + 45*x^3 + 104*x^2 + 109*x + 106, x^75 + 41*x^73 + 98*x^72 + 98*x^71 + 88*x^70 + 26*x^69 + 12*x^68 + 69*x^67 + 24*x^66 + 101*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 34*x^7 + 88*x^6 + 90*x^5 + 12*x^4 + 109*x^3 + 24*x^2 + 77*x + 2, x^75 + 41*x^73 + 118*x^72 + 50*x^71 + 40*x^70 + 10*x^69 + 4*x^68 + 117*x^67 + 104*x^66 + 117*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 114*x^7 + 40*x^6 + 74*x^5 + 4*x^4 + 29*x^3 + 104*x^2 + 93*x + 22, x^75 + 41*x^73 + 98*x^72 + 82*x^71 + 104*x^70 + 10*x^69 + 92*x^68 + 21*x^67 + 72*x^66 + 53*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 18*x^7 + 104*x^6 + 74*x^5 + 92*x^4 + 61*x^3 + 72*x^2 + 29*x + 114, x^75 + 41*x^73 + 82*x^72 + 18*x^71 + 40*x^70 + 74*x^69 + 124*x^68 + 85*x^67 + 8*x^66 + 117*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 82*x^7 + 40*x^6 + 10*x^5 + 124*x^4 + 125*x^3 + 8*x^2 + 93*x + 98, x^75 + 41*x^73 + 58*x^72 + 114*x^71 + 56*x^70 + 74*x^69 + 60*x^68 + 53*x^67 + 56*x^66 + 53*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 50*x^7 + 56*x^6 + 10*x^5 + 60*x^4 + 93*x^3 + 56*x^2 + 29*x + 122, x^75 + 41*x^73 + 114*x^72 + 34*x^71 + 56*x^70 + 90*x^69 + 12*x^68 + 5*x^67 + 56*x^66 + 37*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 98*x^7 + 56*x^6 + 26*x^5 + 12*x^4 + 45*x^3 + 56*x^2 + 13*x + 114, x^75 + 41*x^73 + 14*x^72 + 98*x^71 + 72*x^70 + 26*x^69 + 116*x^68 + 69*x^67 + 72*x^66 + 101*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 34*x^7 + 72*x^6 + 90*x^5 + 116*x^4 + 109*x^3 + 72*x^2 + 77*x + 14, x^75 + 41*x^73 + 38*x^72 + 98*x^71 + 88*x^70 + 122*x^69 + 20*x^68 + 5*x^67 + 120*x^66 + 69*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 34*x^7 + 88*x^6 + 58*x^5 + 20*x^4 + 45*x^3 + 120*x^2 + 45*x + 22, x^75 + 41*x^73 + 98*x^72 + 114*x^71 + 8*x^70 + 106*x^69 + 60*x^68 + 117*x^67 + 40*x^66 + 85*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 50*x^7 + 8*x^6 + 42*x^5 + 60*x^4 + 29*x^3 + 40*x^2 + 61*x + 18, x^75 + 41*x^73 + 70*x^72 + 98*x^71 + 56*x^70 + 122*x^69 + 52*x^68 + 5*x^67 + 24*x^66 + 69*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 34*x^7 + 56*x^6 + 58*x^5 + 52*x^4 + 45*x^3 + 24*x^2 + 45*x + 86, x^75 + 41*x^73 + 26*x^72 + 18*x^71 + 56*x^70 + 106*x^69 + 124*x^68 + 21*x^67 + 56*x^66 + 21*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 82*x^7 + 56*x^6 + 42*x^5 + 124*x^4 + 61*x^3 + 56*x^2 + 125*x + 90, x^75 + 41*x^73 + 42*x^72 + 82*x^71 + 120*x^70 + 42*x^69 + 92*x^68 + 85*x^67 + 120*x^66 + 85*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 18*x^7 + 120*x^6 + 106*x^5 + 92*x^4 + 125*x^3 + 120*x^2 + 61*x + 106, x^75 + 41*x^73 + 106*x^72 + 18*x^71 + 88*x^70 + 42*x^69 + 124*x^68 + 21*x^67 + 24*x^66 + 85*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 82*x^7 + 88*x^6 + 106*x^5 + 124*x^4 + 61*x^3 + 24*x^2 + 61*x + 10, x^75 + 41*x^73 + 122*x^72 + 2*x^71 + 72*x^70 + 26*x^69 + 76*x^68 + 101*x^67 + 104*x^66 + 37*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 66*x^7 + 72*x^6 + 90*x^5 + 76*x^4 + 13*x^3 + 104*x^2 + 13*x + 106, x^75 + 41*x^73 + 58*x^72 + 50*x^71 + 24*x^70 + 74*x^69 + 92*x^68 + 117*x^67 + 88*x^66 + 53*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 114*x^7 + 24*x^6 + 10*x^5 + 92*x^4 + 29*x^3 + 88*x^2 + 29*x + 90, x^75 + 41*x^73 + 70*x^72 + 34*x^71 + 88*x^70 + 122*x^69 + 20*x^68 + 69*x^67 + 120*x^66 + 69*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 98*x^7 + 88*x^6 + 58*x^5 + 20*x^4 + 109*x^3 + 120*x^2 + 45*x + 118, x^75 + 41*x^73 + 106*x^72 + 50*x^71 + 56*x^70 + 74*x^69 + 92*x^68 + 117*x^67 + 56*x^66 + 53*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 114*x^7 + 56*x^6 + 10*x^5 + 92*x^4 + 29*x^3 + 56*x^2 + 29*x + 42, x^75 + 41*x^73 + 2*x^72 + 98*x^71 + 88*x^70 + 26*x^69 + 76*x^68 + 69*x^67 + 24*x^66 + 101*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 34*x^7 + 88*x^6 + 90*x^5 + 76*x^4 + 109*x^3 + 24*x^2 + 77*x + 34, x^75 + 41*x^73 + 122*x^72 + 50*x^71 + 56*x^70 + 74*x^69 + 124*x^68 + 117*x^67 + 56*x^66 + 53*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 114*x^7 + 56*x^6 + 10*x^5 + 124*x^4 + 29*x^3 + 56*x^2 + 29*x + 122, x^75 + 41*x^73 + 126*x^72 + 50*x^71 + 24*x^70 + 106*x^69 + 100*x^68 + 53*x^67 + 56*x^66 + 85*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 114*x^7 + 24*x^6 + 42*x^5 + 100*x^4 + 93*x^3 + 56*x^2 + 61*x + 110, x^75 + 41*x^73 + 10*x^72 + 2*x^71 + 40*x^70 + 90*x^69 + 12*x^68 + 101*x^67 + 8*x^66 + 101*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 66*x^7 + 40*x^6 + 26*x^5 + 12*x^4 + 13*x^3 + 8*x^2 + 77*x + 26, x^75 + 41*x^73 + 54*x^72 + 2*x^71 + 24*x^70 + 26*x^69 + 116*x^68 + 101*x^67 + 56*x^66 + 37*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 66*x^7 + 24*x^6 + 90*x^5 + 116*x^4 + 13*x^3 + 56*x^2 + 13*x + 38, x^75 + 41*x^73 + 18*x^72 + 2*x^71 + 24*x^70 + 58*x^69 + 44*x^68 + 37*x^67 + 88*x^66 + 69*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 66*x^7 + 24*x^6 + 122*x^5 + 44*x^4 + 77*x^3 + 88*x^2 + 45*x + 50, x^75 + 41*x^73 + 122*x^72 + 2*x^71 + 72*x^70 + 90*x^69 + 12*x^68 + 101*x^67 + 104*x^66 + 101*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 66*x^7 + 72*x^6 + 26*x^5 + 12*x^4 + 13*x^3 + 104*x^2 + 77*x + 42, x^75 + 41*x^73 + 6*x^72 + 50*x^71 + 8*x^70 + 10*x^69 + 4*x^68 + 117*x^67 + 8*x^66 + 117*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 114*x^7 + 8*x^6 + 74*x^5 + 4*x^4 + 29*x^3 + 8*x^2 + 93*x + 6, x^75 + 41*x^73 + 70*x^72 + 2*x^71 + 24*x^70 + 26*x^69 + 20*x^68 + 101*x^67 + 56*x^66 + 37*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 66*x^7 + 24*x^6 + 90*x^5 + 20*x^4 + 13*x^3 + 56*x^2 + 13*x + 118, x^75 + 41*x^73 + 122*x^72 + 98*x^71 + 72*x^70 + 58*x^69 + 12*x^68 + 5*x^67 + 104*x^66 + 5*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 34*x^7 + 72*x^6 + 122*x^5 + 12*x^4 + 45*x^3 + 104*x^2 + 109*x + 42, x^75 + 41*x^73 + 26*x^72 + 98*x^71 + 40*x^70 + 58*x^69 + 44*x^68 + 5*x^67 + 8*x^66 + 5*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 34*x^7 + 40*x^6 + 122*x^5 + 44*x^4 + 45*x^3 + 8*x^2 + 109*x + 106, x^75 + 41*x^73 + 94*x^72 + 98*x^71 + 8*x^70 + 90*x^69 + 20*x^68 + 69*x^67 + 8*x^66 + 37*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 34*x^7 + 8*x^6 + 26*x^5 + 20*x^4 + 109*x^3 + 8*x^2 + 13*x + 30, x^75 + 41*x^73 + 30*x^72 + 50*x^71 + 88*x^70 + 42*x^69 + 36*x^68 + 53*x^67 + 120*x^66 + 21*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 114*x^7 + 88*x^6 + 106*x^5 + 36*x^4 + 93*x^3 + 120*x^2 + 125*x + 14, x^75 + 41*x^73 + 30*x^72 + 66*x^71 + 8*x^70 + 122*x^69 + 84*x^68 + 101*x^67 + 8*x^66 + 5*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 2*x^7 + 8*x^6 + 58*x^5 + 84*x^4 + 13*x^3 + 8*x^2 + 109*x + 30, x^75 + 41*x^73 + 122*x^72 + 114*x^71 + 56*x^70 + 74*x^69 + 60*x^68 + 53*x^67 + 56*x^66 + 53*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 50*x^7 + 56*x^6 + 10*x^5 + 60*x^4 + 93*x^3 + 56*x^2 + 29*x + 58, x^75 + 41*x^73 + 66*x^72 + 82*x^71 + 8*x^70 + 74*x^69 + 124*x^68 + 21*x^67 + 40*x^66 + 117*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 18*x^7 + 8*x^6 + 10*x^5 + 124*x^4 + 61*x^3 + 40*x^2 + 93*x + 114, x^75 + 41*x^73 + 46*x^72 + 98*x^71 + 40*x^70 + 26*x^69 + 20*x^68 + 69*x^67 + 104*x^66 + 101*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 34*x^7 + 40*x^6 + 90*x^5 + 20*x^4 + 109*x^3 + 104*x^2 + 77*x + 78, x^75 + 41*x^73 + 122*x^72 + 50*x^71 + 88*x^70 + 74*x^69 + 28*x^68 + 117*x^67 + 24*x^66 + 53*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 114*x^7 + 88*x^6 + 10*x^5 + 28*x^4 + 29*x^3 + 24*x^2 + 29*x + 90, x^75 + 41*x^73 + 94*x^72 + 50*x^71 + 24*x^70 + 42*x^69 + 100*x^68 + 53*x^67 + 56*x^66 + 21*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 114*x^7 + 24*x^6 + 106*x^5 + 100*x^4 + 93*x^3 + 56*x^2 + 125*x + 14, x^75 + 41*x^73 + 94*x^72 + 82*x^71 + 120*x^70 + 74*x^69 + 68*x^68 + 21*x^67 + 88*x^66 + 117*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 18*x^7 + 120*x^6 + 10*x^5 + 68*x^4 + 61*x^3 + 88*x^2 + 93*x + 46, x^75 + 41*x^73 + 62*x^72 + 50*x^71 + 56*x^70 + 42*x^69 + 68*x^68 + 53*x^67 + 24*x^66 + 21*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 114*x^7 + 56*x^6 + 106*x^5 + 68*x^4 + 93*x^3 + 24*x^2 + 125*x + 78, x^75 + 41*x^73 + 74*x^72 + 18*x^71 + 56*x^70 + 106*x^69 + 92*x^68 + 21*x^67 + 56*x^66 + 21*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 82*x^7 + 56*x^6 + 42*x^5 + 92*x^4 + 61*x^3 + 56*x^2 + 125*x + 74, x^75 + 41*x^73 + 62*x^72 + 50*x^71 + 120*x^70 + 106*x^69 + 68*x^68 + 53*x^67 + 88*x^66 + 85*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 114*x^7 + 120*x^6 + 42*x^5 + 68*x^4 + 93*x^3 + 88*x^2 + 61*x + 78, x^75 + 41*x^73 + 78*x^72 + 2*x^71 + 104*x^70 + 122*x^69 + 84*x^68 + 37*x^67 + 40*x^66 + 5*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 66*x^7 + 104*x^6 + 58*x^5 + 84*x^4 + 77*x^3 + 40*x^2 + 109*x + 110, x^75 + 41*x^73 + 10*x^72 + 82*x^71 + 120*x^70 + 42*x^69 + 28*x^68 + 85*x^67 + 120*x^66 + 85*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 18*x^7 + 120*x^6 + 106*x^5 + 28*x^4 + 125*x^3 + 120*x^2 + 61*x + 74, x^75 + 41*x^73 + 102*x^72 + 114*x^71 + 72*x^70 + 10*x^69 + 68*x^68 + 53*x^67 + 72*x^66 + 117*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 50*x^7 + 72*x^6 + 74*x^5 + 68*x^4 + 93*x^3 + 72*x^2 + 93*x + 102, x^75 + 41*x^73 + 82*x^72 + 50*x^71 + 40*x^70 + 106*x^69 + 124*x^68 + 53*x^67 + 8*x^66 + 85*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 114*x^7 + 40*x^6 + 42*x^5 + 124*x^4 + 93*x^3 + 8*x^2 + 61*x + 98, x^75 + 41*x^73 + 122*x^72 + 66*x^71 + 8*x^70 + 26*x^69 + 76*x^68 + 37*x^67 + 40*x^66 + 37*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 2*x^7 + 8*x^6 + 90*x^5 + 76*x^4 + 77*x^3 + 40*x^2 + 13*x + 106, x^75 + 41*x^73 + 30*x^72 + 2*x^71 + 40*x^70 + 58*x^69 + 116*x^68 + 37*x^67 + 104*x^66 + 69*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 66*x^7 + 40*x^6 + 122*x^5 + 116*x^4 + 77*x^3 + 104*x^2 + 45*x + 126, x^75 + 41*x^73 + 110*x^72 + 34*x^71 + 104*x^70 + 90*x^69 + 84*x^68 + 5*x^67 + 40*x^66 + 37*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 98*x^7 + 104*x^6 + 26*x^5 + 84*x^4 + 45*x^3 + 40*x^2 + 13*x + 78, x^75 + 41*x^73 + 62*x^72 + 18*x^71 + 56*x^70 + 10*x^69 + 68*x^68 + 85*x^67 + 24*x^66 + 53*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 82*x^7 + 56*x^6 + 74*x^5 + 68*x^4 + 125*x^3 + 24*x^2 + 29*x + 78, x^75 + 41*x^73 + 42*x^72 + 2*x^71 + 8*x^70 + 90*x^69 + 44*x^68 + 101*x^67 + 40*x^66 + 101*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 66*x^7 + 8*x^6 + 26*x^5 + 44*x^4 + 13*x^3 + 40*x^2 + 77*x + 90, x^75 + 41*x^73 + 10*x^72 + 114*x^71 + 120*x^70 + 10*x^69 + 92*x^68 + 53*x^67 + 120*x^66 + 117*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 50*x^7 + 120*x^6 + 74*x^5 + 92*x^4 + 93*x^3 + 120*x^2 + 93*x + 10, x^75 + 41*x^73 + 18*x^72 + 18*x^71 + 40*x^70 + 74*x^69 + 124*x^68 + 85*x^67 + 8*x^66 + 117*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 82*x^7 + 40*x^6 + 10*x^5 + 124*x^4 + 125*x^3 + 8*x^2 + 93*x + 34, x^75 + 41*x^73 + 62*x^72 + 82*x^71 + 120*x^70 + 74*x^69 + 4*x^68 + 21*x^67 + 88*x^66 + 117*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 18*x^7 + 120*x^6 + 10*x^5 + 4*x^4 + 61*x^3 + 88*x^2 + 93*x + 14, x^75 + 41*x^73 + 22*x^72 + 82*x^71 + 72*x^70 + 42*x^69 + 100*x^68 + 85*x^67 + 72*x^66 + 85*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 18*x^7 + 72*x^6 + 106*x^5 + 100*x^4 + 125*x^3 + 72*x^2 + 61*x + 22, x^75 + 41*x^73 + 34*x^72 + 82*x^71 + 40*x^70 + 10*x^69 + 28*x^68 + 21*x^67 + 8*x^66 + 53*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 18*x^7 + 40*x^6 + 74*x^5 + 28*x^4 + 61*x^3 + 8*x^2 + 29*x + 114, x^75 + 41*x^73 + 70*x^72 + 50*x^71 + 72*x^70 + 74*x^69 + 4*x^68 + 117*x^67 + 72*x^66 + 53*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 114*x^7 + 72*x^6 + 10*x^5 + 4*x^4 + 29*x^3 + 72*x^2 + 29*x + 70, x^75 + 41*x^73 + 102*x^72 + 66*x^71 + 88*x^70 + 26*x^69 + 84*x^68 + 37*x^67 + 120*x^66 + 37*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 2*x^7 + 88*x^6 + 90*x^5 + 84*x^4 + 77*x^3 + 120*x^2 + 13*x + 22, x^75 + 41*x^73 + 38*x^72 + 18*x^71 + 40*x^70 + 106*x^69 + 100*x^68 + 21*x^67 + 104*x^66 + 21*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 82*x^7 + 40*x^6 + 42*x^5 + 100*x^4 + 61*x^3 + 104*x^2 + 125*x + 6, x^75 + 41*x^73 + 54*x^72 + 114*x^71 + 72*x^70 + 10*x^69 + 100*x^68 + 53*x^67 + 72*x^66 + 117*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 50*x^7 + 72*x^6 + 74*x^5 + 100*x^4 + 93*x^3 + 72*x^2 + 93*x + 118, x^75 + 41*x^73 + 22*x^72 + 82*x^71 + 72*x^70 + 106*x^69 + 36*x^68 + 85*x^67 + 72*x^66 + 21*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 18*x^7 + 72*x^6 + 42*x^5 + 36*x^4 + 125*x^3 + 72*x^2 + 125*x + 86, x^75 + 41*x^73 + 74*x^72 + 50*x^71 + 88*x^70 + 10*x^69 + 124*x^68 + 117*x^67 + 24*x^66 + 117*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 114*x^7 + 88*x^6 + 74*x^5 + 124*x^4 + 29*x^3 + 24*x^2 + 93*x + 42, x^75 + 41*x^73 + 38*x^72 + 114*x^71 + 8*x^70 + 10*x^69 + 4*x^68 + 53*x^67 + 8*x^66 + 117*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 50*x^7 + 8*x^6 + 74*x^5 + 4*x^4 + 93*x^3 + 8*x^2 + 93*x + 102, x^75 + 41*x^73 + 78*x^72 + 114*x^71 + 56*x^70 + 106*x^69 + 100*x^68 + 117*x^67 + 24*x^66 + 85*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 50*x^7 + 56*x^6 + 42*x^5 + 100*x^4 + 29*x^3 + 24*x^2 + 61*x + 30, x^75 + 41*x^73 + 114*x^72 + 82*x^71 + 72*x^70 + 10*x^69 + 92*x^68 + 21*x^67 + 104*x^66 + 53*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 18*x^7 + 72*x^6 + 74*x^5 + 92*x^4 + 61*x^3 + 104*x^2 + 29*x + 98, x^75 + 41*x^73 + 2*x^72 + 114*x^71 + 72*x^70 + 106*x^69 + 60*x^68 + 117*x^67 + 104*x^66 + 85*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 50*x^7 + 72*x^6 + 42*x^5 + 60*x^4 + 29*x^3 + 104*x^2 + 61*x + 114, x^75 + 41*x^73 + 94*x^72 + 98*x^71 + 72*x^70 + 90*x^69 + 84*x^68 + 69*x^67 + 72*x^66 + 37*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 34*x^7 + 72*x^6 + 26*x^5 + 84*x^4 + 109*x^3 + 72*x^2 + 13*x + 94, x^75 + 41*x^73 + 46*x^72 + 50*x^71 + 56*x^70 + 106*x^69 + 100*x^68 + 53*x^67 + 24*x^66 + 85*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 114*x^7 + 56*x^6 + 42*x^5 + 100*x^4 + 93*x^3 + 24*x^2 + 61*x + 62, x^75 + 41*x^73 + 54*x^72 + 82*x^71 + 104*x^70 + 42*x^69 + 68*x^68 + 85*x^67 + 40*x^66 + 85*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 18*x^7 + 104*x^6 + 106*x^5 + 68*x^4 + 125*x^3 + 40*x^2 + 61*x + 22, x^75 + 41*x^73 + 114*x^72 + 2*x^71 + 24*x^70 + 58*x^69 + 108*x^68 + 37*x^67 + 88*x^66 + 69*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 66*x^7 + 24*x^6 + 122*x^5 + 108*x^4 + 77*x^3 + 88*x^2 + 45*x + 18, x^75 + 41*x^73 + 62*x^72 + 34*x^71 + 40*x^70 + 26*x^69 + 116*x^68 + 5*x^67 + 104*x^66 + 101*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 98*x^7 + 40*x^6 + 90*x^5 + 116*x^4 + 45*x^3 + 104*x^2 + 77*x + 94, x^75 + 41*x^73 + 106*x^72 + 34*x^71 + 72*x^70 + 122*x^69 + 108*x^68 + 69*x^67 + 104*x^66 + 69*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 98*x^7 + 72*x^6 + 58*x^5 + 108*x^4 + 109*x^3 + 104*x^2 + 45*x + 90, x^75 + 41*x^73 + 14*x^72 + 66*x^71 + 104*x^70 + 58*x^69 + 84*x^68 + 101*x^67 + 40*x^66 + 69*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 2*x^7 + 104*x^6 + 122*x^5 + 84*x^4 + 13*x^3 + 40*x^2 + 45*x + 46, x^75 + 41*x^73 + 58*x^72 + 66*x^71 + 72*x^70 + 90*x^69 + 76*x^68 + 37*x^67 + 104*x^66 + 101*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 2*x^7 + 72*x^6 + 26*x^5 + 76*x^4 + 77*x^3 + 104*x^2 + 77*x + 42, x^75 + 41*x^73 + 110*x^72 + 98*x^71 + 72*x^70 + 90*x^69 + 116*x^68 + 69*x^67 + 72*x^66 + 37*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 34*x^7 + 72*x^6 + 26*x^5 + 116*x^4 + 109*x^3 + 72*x^2 + 13*x + 46, x^75 + 41*x^73 + 22*x^72 + 82*x^71 + 104*x^70 + 42*x^69 + 4*x^68 + 85*x^67 + 40*x^66 + 85*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 18*x^7 + 104*x^6 + 106*x^5 + 4*x^4 + 125*x^3 + 40*x^2 + 61*x + 118, x^75 + 41*x^73 + 90*x^72 + 98*x^71 + 104*x^70 + 58*x^69 + 108*x^68 + 5*x^67 + 72*x^66 + 5*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 34*x^7 + 104*x^6 + 122*x^5 + 108*x^4 + 45*x^3 + 72*x^2 + 109*x + 106, x^75 + 41*x^73 + 90*x^72 + 66*x^71 + 72*x^70 + 90*x^69 + 12*x^68 + 37*x^67 + 104*x^66 + 101*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 2*x^7 + 72*x^6 + 26*x^5 + 12*x^4 + 77*x^3 + 104*x^2 + 77*x + 74, x^75 + 41*x^73 + 34*x^72 + 50*x^71 + 8*x^70 + 106*x^69 + 124*x^68 + 53*x^67 + 40*x^66 + 85*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 114*x^7 + 8*x^6 + 42*x^5 + 124*x^4 + 93*x^3 + 40*x^2 + 61*x + 18, x^75 + 41*x^73 + 38*x^72 + 34*x^71 + 24*x^70 + 58*x^69 + 84*x^68 + 69*x^67 + 56*x^66 + 5*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 98*x^7 + 24*x^6 + 122*x^5 + 84*x^4 + 109*x^3 + 56*x^2 + 109*x + 86, x^75 + 41*x^73 + 82*x^72 + 18*x^71 + 40*x^70 + 10*x^69 + 60*x^68 + 85*x^67 + 8*x^66 + 53*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 82*x^7 + 40*x^6 + 74*x^5 + 60*x^4 + 125*x^3 + 8*x^2 + 29*x + 34, x^75 + 41*x^73 + 62*x^72 + 98*x^71 + 8*x^70 + 90*x^69 + 84*x^68 + 69*x^67 + 8*x^66 + 37*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 34*x^7 + 8*x^6 + 26*x^5 + 84*x^4 + 109*x^3 + 8*x^2 + 13*x + 126, x^75 + 41*x^73 + 18*x^72 + 50*x^71 + 104*x^70 + 42*x^69 + 124*x^68 + 53*x^67 + 72*x^66 + 21*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 114*x^7 + 104*x^6 + 106*x^5 + 124*x^4 + 93*x^3 + 72*x^2 + 125*x + 34, x^75 + 41*x^73 + 62*x^72 + 18*x^71 + 24*x^70 + 10*x^69 + 36*x^68 + 85*x^67 + 56*x^66 + 53*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 82*x^7 + 24*x^6 + 74*x^5 + 36*x^4 + 125*x^3 + 56*x^2 + 29*x + 110, x^75 + 41*x^73 + 122*x^72 + 18*x^71 + 88*x^70 + 42*x^69 + 28*x^68 + 21*x^67 + 24*x^66 + 85*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 82*x^7 + 88*x^6 + 106*x^5 + 28*x^4 + 61*x^3 + 24*x^2 + 61*x + 90, x^75 + 41*x^73 + 42*x^72 + 114*x^71 + 120*x^70 + 10*x^69 + 28*x^68 + 53*x^67 + 120*x^66 + 117*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 50*x^7 + 120*x^6 + 74*x^5 + 28*x^4 + 93*x^3 + 120*x^2 + 93*x + 42, x^75 + 41*x^73 + 46*x^72 + 2*x^71 + 72*x^70 + 58*x^69 + 52*x^68 + 37*x^67 + 72*x^66 + 69*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 66*x^7 + 72*x^6 + 122*x^5 + 52*x^4 + 77*x^3 + 72*x^2 + 45*x + 46, x^75 + 41*x^73 + 26*x^72 + 34*x^71 + 40*x^70 + 58*x^69 + 108*x^68 + 69*x^67 + 8*x^66 + 5*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 98*x^7 + 40*x^6 + 122*x^5 + 108*x^4 + 109*x^3 + 8*x^2 + 109*x + 42, x^75 + 41*x^73 + 42*x^72 + 66*x^71 + 40*x^70 + 26*x^69 + 76*x^68 + 37*x^67 + 8*x^66 + 37*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 2*x^7 + 40*x^6 + 90*x^5 + 76*x^4 + 77*x^3 + 8*x^2 + 13*x + 58, x^75 + 41*x^73 + 34*x^72 + 2*x^71 + 120*x^70 + 58*x^69 + 44*x^68 + 37*x^67 + 120*x^66 + 69*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 66*x^7 + 120*x^6 + 122*x^5 + 44*x^4 + 77*x^3 + 120*x^2 + 45*x + 34, x^75 + 41*x^73 + 46*x^72 + 34*x^71 + 104*x^70 + 26*x^69 + 20*x^68 + 5*x^67 + 40*x^66 + 101*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 98*x^7 + 104*x^6 + 90*x^5 + 20*x^4 + 45*x^3 + 40*x^2 + 77*x + 78, x^75 + 41*x^73 + 46*x^72 + 82*x^71 + 24*x^70 + 10*x^69 + 68*x^68 + 21*x^67 + 56*x^66 + 53*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 18*x^7 + 24*x^6 + 74*x^5 + 68*x^4 + 61*x^3 + 56*x^2 + 29*x + 94, x^75 + 41*x^73 + 98*x^72 + 18*x^71 + 8*x^70 + 74*x^69 + 124*x^68 + 85*x^67 + 40*x^66 + 117*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 82*x^7 + 8*x^6 + 10*x^5 + 124*x^4 + 125*x^3 + 40*x^2 + 93*x + 82, x^75 + 41*x^73 + 102*x^72 + 98*x^71 + 120*x^70 + 122*x^69 + 52*x^68 + 5*x^67 + 88*x^66 + 69*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 34*x^7 + 120*x^6 + 58*x^5 + 52*x^4 + 45*x^3 + 88*x^2 + 45*x + 54, x^75 + 41*x^73 + 42*x^72 + 82*x^71 + 56*x^70 + 106*x^69 + 92*x^68 + 85*x^67 + 56*x^66 + 21*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 18*x^7 + 56*x^6 + 42*x^5 + 92*x^4 + 125*x^3 + 56*x^2 + 125*x + 106, x^75 + 41*x^73 + 94*x^72 + 50*x^71 + 120*x^70 + 106*x^69 + 4*x^68 + 53*x^67 + 88*x^66 + 85*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 114*x^7 + 120*x^6 + 42*x^5 + 4*x^4 + 93*x^3 + 88*x^2 + 61*x + 110, x^75 + 41*x^73 + 34*x^72 + 2*x^71 + 88*x^70 + 122*x^69 + 76*x^68 + 37*x^67 + 24*x^66 + 5*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 66*x^7 + 88*x^6 + 58*x^5 + 76*x^4 + 77*x^3 + 24*x^2 + 109*x + 2, x^75 + 41*x^73 + 106*x^72 + 98*x^71 + 104*x^70 + 122*x^69 + 76*x^68 + 5*x^67 + 72*x^66 + 69*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 34*x^7 + 104*x^6 + 58*x^5 + 76*x^4 + 45*x^3 + 72*x^2 + 45*x + 122, x^75 + 41*x^73 + 114*x^72 + 82*x^71 + 104*x^70 + 10*x^69 + 124*x^68 + 21*x^67 + 72*x^66 + 53*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 18*x^7 + 104*x^6 + 74*x^5 + 124*x^4 + 61*x^3 + 72*x^2 + 29*x + 66, x^75 + 41*x^73 + 14*x^72 + 114*x^71 + 56*x^70 + 42*x^69 + 36*x^68 + 117*x^67 + 24*x^66 + 21*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 50*x^7 + 56*x^6 + 106*x^5 + 36*x^4 + 29*x^3 + 24*x^2 + 125*x + 30, x^75 + 41*x^73 + 82*x^72 + 82*x^71 + 72*x^70 + 10*x^69 + 28*x^68 + 21*x^67 + 104*x^66 + 53*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 18*x^7 + 72*x^6 + 74*x^5 + 28*x^4 + 61*x^3 + 104*x^2 + 29*x + 66, x^75 + 41*x^73 + 66*x^72 + 98*x^71 + 120*x^70 + 26*x^69 + 108*x^68 + 69*x^67 + 120*x^66 + 101*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 34*x^7 + 120*x^6 + 90*x^5 + 108*x^4 + 109*x^3 + 120*x^2 + 77*x + 66, x^75 + 41*x^73 + 22*x^72 + 114*x^71 + 8*x^70 + 10*x^69 + 100*x^68 + 53*x^67 + 8*x^66 + 117*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 50*x^7 + 8*x^6 + 74*x^5 + 100*x^4 + 93*x^3 + 8*x^2 + 93*x + 22, x^75 + 41*x^73 + 54*x^72 + 114*x^71 + 8*x^70 + 10*x^69 + 36*x^68 + 53*x^67 + 8*x^66 + 117*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 50*x^7 + 8*x^6 + 74*x^5 + 36*x^4 + 93*x^3 + 8*x^2 + 93*x + 54, x^75 + 41*x^73 + 50*x^72 + 50*x^71 + 104*x^70 + 106*x^69 + 124*x^68 + 53*x^67 + 72*x^66 + 85*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 114*x^7 + 104*x^6 + 42*x^5 + 124*x^4 + 93*x^3 + 72*x^2 + 61*x + 2, x^75 + 41*x^73 + 10*x^72 + 66*x^71 + 72*x^70 + 90*x^69 + 108*x^68 + 37*x^67 + 104*x^66 + 101*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 2*x^7 + 72*x^6 + 26*x^5 + 108*x^4 + 77*x^3 + 104*x^2 + 77*x + 58, x^75 + 41*x^73 + 38*x^72 + 2*x^71 + 56*x^70 + 90*x^69 + 52*x^68 + 101*x^67 + 24*x^66 + 101*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 66*x^7 + 56*x^6 + 26*x^5 + 52*x^4 + 13*x^3 + 24*x^2 + 77*x + 118, x^75 + 41*x^73 + 46*x^72 + 82*x^71 + 88*x^70 + 74*x^69 + 68*x^68 + 21*x^67 + 120*x^66 + 117*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 18*x^7 + 88*x^6 + 10*x^5 + 68*x^4 + 61*x^3 + 120*x^2 + 93*x + 94, x^75 + 41*x^73 + 2*x^72 + 50*x^71 + 40*x^70 + 42*x^69 + 28*x^68 + 53*x^67 + 8*x^66 + 21*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 114*x^7 + 40*x^6 + 106*x^5 + 28*x^4 + 93*x^3 + 8*x^2 + 125*x + 18, x^75 + 41*x^73 + 78*x^72 + 2*x^71 + 40*x^70 + 122*x^69 + 20*x^68 + 37*x^67 + 104*x^66 + 5*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 66*x^7 + 40*x^6 + 58*x^5 + 20*x^4 + 77*x^3 + 104*x^2 + 109*x + 46, x^75 + 41*x^73 + 74*x^72 + 18*x^71 + 24*x^70 + 106*x^69 + 60*x^68 + 21*x^67 + 88*x^66 + 21*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 82*x^7 + 24*x^6 + 42*x^5 + 60*x^4 + 61*x^3 + 88*x^2 + 125*x + 106, x^75 + 41*x^73 + 58*x^72 + 114*x^71 + 120*x^70 + 10*x^69 + 60*x^68 + 53*x^67 + 120*x^66 + 117*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 50*x^7 + 120*x^6 + 74*x^5 + 60*x^4 + 93*x^3 + 120*x^2 + 93*x + 122, x^75 + 41*x^73 + 74*x^72 + 114*x^71 + 120*x^70 + 10*x^69 + 92*x^68 + 53*x^67 + 120*x^66 + 117*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 50*x^7 + 120*x^6 + 74*x^5 + 92*x^4 + 93*x^3 + 120*x^2 + 93*x + 74, x^75 + 41*x^73 + 90*x^72 + 98*x^71 + 72*x^70 + 122*x^69 + 12*x^68 + 5*x^67 + 104*x^66 + 69*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 34*x^7 + 72*x^6 + 58*x^5 + 12*x^4 + 45*x^3 + 104*x^2 + 45*x + 74, x^75 + 41*x^73 + 50*x^72 + 50*x^71 + 72*x^70 + 42*x^69 + 28*x^68 + 53*x^67 + 104*x^66 + 21*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 114*x^7 + 72*x^6 + 106*x^5 + 28*x^4 + 93*x^3 + 104*x^2 + 125*x + 98, x^75 + 41*x^73 + 26*x^72 + 114*x^71 + 88*x^70 + 10*x^69 + 92*x^68 + 53*x^67 + 24*x^66 + 117*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 50*x^7 + 88*x^6 + 74*x^5 + 92*x^4 + 93*x^3 + 24*x^2 + 93*x + 122, x^75 + 41*x^73 + 90*x^72 + 2*x^71 + 72*x^70 + 90*x^69 + 76*x^68 + 101*x^67 + 104*x^66 + 101*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 66*x^7 + 72*x^6 + 26*x^5 + 76*x^4 + 13*x^3 + 104*x^2 + 77*x + 10, x^75 + 41*x^73 + 54*x^72 + 114*x^71 + 72*x^70 + 74*x^69 + 36*x^68 + 53*x^67 + 72*x^66 + 53*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 50*x^7 + 72*x^6 + 10*x^5 + 36*x^4 + 93*x^3 + 72*x^2 + 29*x + 54, x^75 + 41*x^73 + 86*x^72 + 2*x^71 + 56*x^70 + 90*x^69 + 20*x^68 + 101*x^67 + 24*x^66 + 101*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 66*x^7 + 56*x^6 + 26*x^5 + 20*x^4 + 13*x^3 + 24*x^2 + 77*x + 102, x^75 + 41*x^73 + 110*x^72 + 2*x^71 + 40*x^70 + 58*x^69 + 20*x^68 + 37*x^67 + 104*x^66 + 69*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 66*x^7 + 40*x^6 + 122*x^5 + 20*x^4 + 77*x^3 + 104*x^2 + 45*x + 14, x^75 + 41*x^73 + 118*x^72 + 82*x^71 + 72*x^70 + 42*x^69 + 36*x^68 + 85*x^67 + 72*x^66 + 85*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 18*x^7 + 72*x^6 + 106*x^5 + 36*x^4 + 125*x^3 + 72*x^2 + 61*x + 118, x^75 + 41*x^73 + 118*x^72 + 98*x^71 + 88*x^70 + 122*x^69 + 52*x^68 + 5*x^67 + 120*x^66 + 69*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 34*x^7 + 88*x^6 + 58*x^5 + 52*x^4 + 45*x^3 + 120*x^2 + 45*x + 38, x^75 + 41*x^73 + 42*x^72 + 82*x^71 + 56*x^70 + 42*x^69 + 28*x^68 + 85*x^67 + 56*x^66 + 85*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 18*x^7 + 56*x^6 + 106*x^5 + 28*x^4 + 125*x^3 + 56*x^2 + 61*x + 42, x^75 + 41*x^73 + 98*x^72 + 50*x^71 + 72*x^70 + 42*x^69 + 124*x^68 + 53*x^67 + 104*x^66 + 21*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 114*x^7 + 72*x^6 + 106*x^5 + 124*x^4 + 93*x^3 + 104*x^2 + 125*x + 82, x^75 + 41*x^73 + 78*x^72 + 82*x^71 + 88*x^70 + 10*x^69 + 68*x^68 + 21*x^67 + 120*x^66 + 53*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 18*x^7 + 88*x^6 + 74*x^5 + 68*x^4 + 61*x^3 + 120*x^2 + 29*x + 62, x^75 + 41*x^73 + 94*x^72 + 18*x^71 + 24*x^70 + 10*x^69 + 100*x^68 + 85*x^67 + 56*x^66 + 53*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 82*x^7 + 24*x^6 + 74*x^5 + 100*x^4 + 125*x^3 + 56*x^2 + 29*x + 14, x^75 + 41*x^73 + 102*x^72 + 82*x^71 + 40*x^70 + 42*x^69 + 100*x^68 + 85*x^67 + 104*x^66 + 85*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 18*x^7 + 40*x^6 + 106*x^5 + 100*x^4 + 125*x^3 + 104*x^2 + 61*x + 70, x^75 + 41*x^73 + 18*x^72 + 82*x^71 + 72*x^70 + 10*x^69 + 28*x^68 + 21*x^67 + 104*x^66 + 53*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 18*x^7 + 72*x^6 + 74*x^5 + 28*x^4 + 61*x^3 + 104*x^2 + 29*x + 2, x^75 + 41*x^73 + 78*x^72 + 2*x^71 + 40*x^70 + 58*x^69 + 84*x^68 + 37*x^67 + 104*x^66 + 69*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 66*x^7 + 40*x^6 + 122*x^5 + 84*x^4 + 77*x^3 + 104*x^2 + 45*x + 110, x^75 + 41*x^73 + 6*x^72 + 2*x^71 + 56*x^70 + 90*x^69 + 116*x^68 + 101*x^67 + 24*x^66 + 101*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 66*x^7 + 56*x^6 + 26*x^5 + 116*x^4 + 13*x^3 + 24*x^2 + 77*x + 86, x^75 + 41*x^73 + 26*x^72 + 98*x^71 + 104*x^70 + 122*x^69 + 44*x^68 + 5*x^67 + 72*x^66 + 69*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 34*x^7 + 104*x^6 + 58*x^5 + 44*x^4 + 45*x^3 + 72*x^2 + 45*x + 106, x^75 + 41*x^73 + 22*x^72 + 66*x^71 + 56*x^70 + 26*x^69 + 20*x^68 + 37*x^67 + 24*x^66 + 37*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 2*x^7 + 56*x^6 + 90*x^5 + 20*x^4 + 77*x^3 + 24*x^2 + 13*x + 38, x^75 + 41*x^73 + 78*x^72 + 66*x^71 + 40*x^70 + 58*x^69 + 20*x^68 + 101*x^67 + 104*x^66 + 69*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 2*x^7 + 40*x^6 + 122*x^5 + 20*x^4 + 13*x^3 + 104*x^2 + 45*x + 46, x^75 + 41*x^73 + 78*x^72 + 18*x^71 + 56*x^70 + 74*x^69 + 36*x^68 + 85*x^67 + 24*x^66 + 117*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 82*x^7 + 56*x^6 + 10*x^5 + 36*x^4 + 125*x^3 + 24*x^2 + 93*x + 94, x^75 + 41*x^73 + 90*x^72 + 18*x^71 + 56*x^70 + 106*x^69 + 124*x^68 + 21*x^67 + 56*x^66 + 21*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 82*x^7 + 56*x^6 + 42*x^5 + 124*x^4 + 61*x^3 + 56*x^2 + 125*x + 26, x^75 + 41*x^73 + 110*x^72 + 82*x^71 + 120*x^70 + 74*x^69 + 100*x^68 + 21*x^67 + 88*x^66 + 117*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 18*x^7 + 120*x^6 + 10*x^5 + 100*x^4 + 61*x^3 + 88*x^2 + 93*x + 126, x^75 + 41*x^73 + 26*x^72 + 18*x^71 + 88*x^70 + 106*x^69 + 28*x^68 + 21*x^67 + 24*x^66 + 21*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 82*x^7 + 88*x^6 + 42*x^5 + 28*x^4 + 61*x^3 + 24*x^2 + 125*x + 58, x^75 + 41*x^73 + 38*x^72 + 114*x^71 + 72*x^70 + 74*x^69 + 4*x^68 + 53*x^67 + 72*x^66 + 53*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 50*x^7 + 72*x^6 + 10*x^5 + 4*x^4 + 93*x^3 + 72*x^2 + 29*x + 102, x^75 + 41*x^73 + 98*x^72 + 34*x^71 + 24*x^70 + 90*x^69 + 76*x^68 + 5*x^67 + 88*x^66 + 37*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 98*x^7 + 24*x^6 + 26*x^5 + 76*x^4 + 45*x^3 + 88*x^2 + 13*x + 66, x^75 + 41*x^73 + 82*x^72 + 34*x^71 + 56*x^70 + 90*x^69 + 76*x^68 + 5*x^67 + 56*x^66 + 37*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 98*x^7 + 56*x^6 + 26*x^5 + 76*x^4 + 45*x^3 + 56*x^2 + 13*x + 82, x^75 + 41*x^73 + 46*x^72 + 34*x^71 + 72*x^70 + 90*x^69 + 52*x^68 + 5*x^67 + 72*x^66 + 37*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 98*x^7 + 72*x^6 + 26*x^5 + 52*x^4 + 45*x^3 + 72*x^2 + 13*x + 46, x^75 + 41*x^73 + 10*x^72 + 114*x^71 + 120*x^70 + 74*x^69 + 28*x^68 + 53*x^67 + 120*x^66 + 53*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 50*x^7 + 120*x^6 + 10*x^5 + 28*x^4 + 93*x^3 + 120*x^2 + 29*x + 74, x^75 + 41*x^73 + 82*x^72 + 82*x^71 + 104*x^70 + 74*x^69 + 124*x^68 + 21*x^67 + 72*x^66 + 117*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 18*x^7 + 104*x^6 + 10*x^5 + 124*x^4 + 61*x^3 + 72*x^2 + 93*x + 98, x^75 + 41*x^73 + 58*x^72 + 98*x^71 + 72*x^70 + 122*x^69 + 76*x^68 + 5*x^67 + 104*x^66 + 69*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 34*x^7 + 72*x^6 + 58*x^5 + 76*x^4 + 45*x^3 + 104*x^2 + 45*x + 42, x^75 + 41*x^73 + 42*x^72 + 50*x^71 + 88*x^70 + 74*x^69 + 124*x^68 + 117*x^67 + 24*x^66 + 53*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 114*x^7 + 88*x^6 + 10*x^5 + 124*x^4 + 29*x^3 + 24*x^2 + 29*x + 74, x^75 + 41*x^73 + 58*x^72 + 82*x^71 + 56*x^70 + 42*x^69 + 60*x^68 + 85*x^67 + 56*x^66 + 85*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 18*x^7 + 56*x^6 + 106*x^5 + 60*x^4 + 125*x^3 + 56*x^2 + 61*x + 122, x^75 + 41*x^73 + 78*x^72 + 18*x^71 + 24*x^70 + 74*x^69 + 4*x^68 + 85*x^67 + 56*x^66 + 117*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 82*x^7 + 24*x^6 + 10*x^5 + 4*x^4 + 125*x^3 + 56*x^2 + 93*x + 126, x^75 + 41*x^73 + 18*x^72 + 34*x^71 + 88*x^70 + 26*x^69 + 44*x^68 + 5*x^67 + 24*x^66 + 101*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 98*x^7 + 88*x^6 + 90*x^5 + 44*x^4 + 45*x^3 + 24*x^2 + 77*x + 50, x^75 + 41*x^73 + 98*x^72 + 66*x^71 + 120*x^70 + 122*x^69 + 44*x^68 + 101*x^67 + 120*x^66 + 5*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 2*x^7 + 120*x^6 + 58*x^5 + 44*x^4 + 13*x^3 + 120*x^2 + 109*x + 98, x^75 + 41*x^73 + 66*x^72 + 114*x^71 + 8*x^70 + 106*x^69 + 124*x^68 + 117*x^67 + 40*x^66 + 85*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 50*x^7 + 8*x^6 + 42*x^5 + 124*x^4 + 29*x^3 + 40*x^2 + 61*x + 114, x^75 + 41*x^73 + 90*x^72 + 66*x^71 + 8*x^70 + 90*x^69 + 76*x^68 + 37*x^67 + 40*x^66 + 101*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 2*x^7 + 8*x^6 + 26*x^5 + 76*x^4 + 77*x^3 + 40*x^2 + 77*x + 10, x^75 + 41*x^73 + 66*x^72 + 82*x^71 + 104*x^70 + 74*x^69 + 92*x^68 + 21*x^67 + 72*x^66 + 117*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 18*x^7 + 104*x^6 + 10*x^5 + 92*x^4 + 61*x^3 + 72*x^2 + 93*x + 18, x^75 + 41*x^73 + 58*x^72 + 50*x^71 + 24*x^70 + 10*x^69 + 28*x^68 + 117*x^67 + 88*x^66 + 117*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 114*x^7 + 24*x^6 + 74*x^5 + 28*x^4 + 29*x^3 + 88*x^2 + 93*x + 26, x^75 + 41*x^73 + 2*x^72 + 2*x^71 + 120*x^70 + 58*x^69 + 108*x^68 + 37*x^67 + 120*x^66 + 69*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 66*x^7 + 120*x^6 + 122*x^5 + 108*x^4 + 77*x^3 + 120*x^2 + 45*x + 2, x^75 + 41*x^73 + 46*x^72 + 66*x^71 + 8*x^70 + 58*x^69 + 52*x^68 + 101*x^67 + 8*x^66 + 69*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 2*x^7 + 8*x^6 + 122*x^5 + 52*x^4 + 13*x^3 + 8*x^2 + 45*x + 46, x^75 + 41*x^73 + 54*x^72 + 114*x^71 + 40*x^70 + 74*x^69 + 4*x^68 + 53*x^67 + 104*x^66 + 53*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 50*x^7 + 40*x^6 + 10*x^5 + 4*x^4 + 93*x^3 + 104*x^2 + 29*x + 86, x^75 + 41*x^73 + 26*x^72 + 66*x^71 + 72*x^70 + 90*x^69 + 12*x^68 + 37*x^67 + 104*x^66 + 101*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 2*x^7 + 72*x^6 + 26*x^5 + 12*x^4 + 77*x^3 + 104*x^2 + 77*x + 10, x^75 + 41*x^73 + 106*x^72 + 50*x^71 + 24*x^70 + 74*x^69 + 60*x^68 + 117*x^67 + 88*x^66 + 53*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 114*x^7 + 24*x^6 + 10*x^5 + 60*x^4 + 29*x^3 + 88*x^2 + 29*x + 74, x^75 + 41*x^73 + 58*x^72 + 18*x^71 + 88*x^70 + 42*x^69 + 28*x^68 + 21*x^67 + 24*x^66 + 85*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 82*x^7 + 88*x^6 + 106*x^5 + 28*x^4 + 61*x^3 + 24*x^2 + 61*x + 26, x^75 + 41*x^73 + 118*x^72 + 2*x^71 + 56*x^70 + 90*x^69 + 84*x^68 + 101*x^67 + 24*x^66 + 101*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 66*x^7 + 56*x^6 + 26*x^5 + 84*x^4 + 13*x^3 + 24*x^2 + 77*x + 6, x^75 + 41*x^73 + 10*x^72 + 18*x^71 + 120*x^70 + 42*x^69 + 92*x^68 + 21*x^67 + 120*x^66 + 85*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 82*x^7 + 120*x^6 + 106*x^5 + 92*x^4 + 61*x^3 + 120*x^2 + 61*x + 10, x^75 + 41*x^73 + 46*x^72 + 18*x^71 + 120*x^70 + 10*x^69 + 100*x^68 + 85*x^67 + 88*x^66 + 53*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 82*x^7 + 120*x^6 + 74*x^5 + 100*x^4 + 125*x^3 + 88*x^2 + 29*x + 62, x^75 + 41*x^73 + 30*x^72 + 98*x^71 + 8*x^70 + 26*x^69 + 84*x^68 + 69*x^67 + 8*x^66 + 101*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 34*x^7 + 8*x^6 + 90*x^5 + 84*x^4 + 109*x^3 + 8*x^2 + 77*x + 30, x^75 + 41*x^73 + 90*x^72 + 66*x^71 + 8*x^70 + 26*x^69 + 12*x^68 + 37*x^67 + 40*x^66 + 37*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 2*x^7 + 8*x^6 + 90*x^5 + 12*x^4 + 77*x^3 + 40*x^2 + 13*x + 74, x^75 + 41*x^73 + 86*x^72 + 114*x^71 + 8*x^70 + 10*x^69 + 100*x^68 + 53*x^67 + 8*x^66 + 117*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 50*x^7 + 8*x^6 + 74*x^5 + 100*x^4 + 93*x^3 + 8*x^2 + 93*x + 86, x^75 + 41*x^73 + 50*x^72 + 50*x^71 + 40*x^70 + 106*x^69 + 60*x^68 + 53*x^67 + 8*x^66 + 85*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 114*x^7 + 40*x^6 + 42*x^5 + 60*x^4 + 93*x^3 + 8*x^2 + 61*x + 66, x^75 + 41*x^73 + 22*x^72 + 18*x^71 + 8*x^70 + 42*x^69 + 100*x^68 + 21*x^67 + 8*x^66 + 85*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 82*x^7 + 8*x^6 + 106*x^5 + 100*x^4 + 61*x^3 + 8*x^2 + 61*x + 22, x^75 + 41*x^73 + 54*x^72 + 98*x^71 + 24*x^70 + 122*x^69 + 116*x^68 + 5*x^67 + 56*x^66 + 69*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 34*x^7 + 24*x^6 + 58*x^5 + 116*x^4 + 45*x^3 + 56*x^2 + 45*x + 38, x^75 + 41*x^73 + 106*x^72 + 18*x^71 + 56*x^70 + 42*x^69 + 92*x^68 + 21*x^67 + 56*x^66 + 85*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 82*x^7 + 56*x^6 + 106*x^5 + 92*x^4 + 61*x^3 + 56*x^2 + 61*x + 42, x^75 + 41*x^73 + 86*x^72 + 66*x^71 + 56*x^70 + 90*x^69 + 84*x^68 + 37*x^67 + 24*x^66 + 101*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 2*x^7 + 56*x^6 + 26*x^5 + 84*x^4 + 77*x^3 + 24*x^2 + 77*x + 38, x^75 + 41*x^73 + 2*x^72 + 50*x^71 + 104*x^70 + 42*x^69 + 92*x^68 + 53*x^67 + 72*x^66 + 21*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 114*x^7 + 104*x^6 + 106*x^5 + 92*x^4 + 93*x^3 + 72*x^2 + 125*x + 82, x^75 + 41*x^73 + 122*x^72 + 66*x^71 + 40*x^70 + 90*x^69 + 44*x^68 + 37*x^67 + 8*x^66 + 101*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 2*x^7 + 40*x^6 + 26*x^5 + 44*x^4 + 77*x^3 + 8*x^2 + 77*x + 10, x^75 + 41*x^73 + 22*x^72 + 66*x^71 + 24*x^70 + 26*x^69 + 116*x^68 + 37*x^67 + 56*x^66 + 37*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 2*x^7 + 24*x^6 + 90*x^5 + 116*x^4 + 77*x^3 + 56*x^2 + 13*x + 70, x^75 + 41*x^73 + 34*x^72 + 82*x^71 + 72*x^70 + 74*x^69 + 124*x^68 + 21*x^67 + 104*x^66 + 117*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 18*x^7 + 72*x^6 + 10*x^5 + 124*x^4 + 61*x^3 + 104*x^2 + 93*x + 18, x^75 + 41*x^73 + 46*x^72 + 82*x^71 + 56*x^70 + 74*x^69 + 36*x^68 + 21*x^67 + 24*x^66 + 117*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 18*x^7 + 56*x^6 + 10*x^5 + 36*x^4 + 61*x^3 + 24*x^2 + 93*x + 126, x^75 + 41*x^73 + 110*x^72 + 66*x^71 + 40*x^70 + 122*x^69 + 20*x^68 + 101*x^67 + 104*x^66 + 5*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 2*x^7 + 40*x^6 + 58*x^5 + 20*x^4 + 13*x^3 + 104*x^2 + 109*x + 14, x^75 + 41*x^73 + 34*x^72 + 2*x^71 + 24*x^70 + 58*x^69 + 76*x^68 + 37*x^67 + 88*x^66 + 69*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 66*x^7 + 24*x^6 + 122*x^5 + 76*x^4 + 77*x^3 + 88*x^2 + 45*x + 2, x^75 + 41*x^73 + 82*x^72 + 66*x^71 + 120*x^70 + 122*x^69 + 12*x^68 + 101*x^67 + 120*x^66 + 5*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 2*x^7 + 120*x^6 + 58*x^5 + 12*x^4 + 13*x^3 + 120*x^2 + 109*x + 18, x^75 + 41*x^73 + 10*x^72 + 114*x^71 + 56*x^70 + 10*x^69 + 28*x^68 + 53*x^67 + 56*x^66 + 117*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 50*x^7 + 56*x^6 + 74*x^5 + 28*x^4 + 93*x^3 + 56*x^2 + 93*x + 74, x^75 + 41*x^73 + 42*x^72 + 114*x^71 + 88*x^70 + 10*x^69 + 124*x^68 + 53*x^67 + 24*x^66 + 117*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 50*x^7 + 88*x^6 + 74*x^5 + 124*x^4 + 93*x^3 + 24*x^2 + 93*x + 74, x^75 + 41*x^73 + 22*x^72 + 66*x^71 + 88*x^70 + 26*x^69 + 52*x^68 + 37*x^67 + 120*x^66 + 37*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 2*x^7 + 88*x^6 + 90*x^5 + 52*x^4 + 77*x^3 + 120*x^2 + 13*x + 6, x^75 + 41*x^73 + 82*x^72 + 50*x^71 + 40*x^70 + 42*x^69 + 60*x^68 + 53*x^67 + 8*x^66 + 21*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 114*x^7 + 40*x^6 + 106*x^5 + 60*x^4 + 93*x^3 + 8*x^2 + 125*x + 34, x^75 + 41*x^73 + 74*x^72 + 34*x^71 + 72*x^70 + 122*x^69 + 44*x^68 + 69*x^67 + 104*x^66 + 69*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 98*x^7 + 72*x^6 + 58*x^5 + 44*x^4 + 109*x^3 + 104*x^2 + 45*x + 58, x^75 + 41*x^73 + 74*x^72 + 2*x^71 + 8*x^70 + 90*x^69 + 108*x^68 + 101*x^67 + 40*x^66 + 101*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 66*x^7 + 8*x^6 + 26*x^5 + 108*x^4 + 13*x^3 + 40*x^2 + 77*x + 122, x^75 + 41*x^73 + 86*x^72 + 114*x^71 + 72*x^70 + 74*x^69 + 100*x^68 + 53*x^67 + 72*x^66 + 53*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 50*x^7 + 72*x^6 + 10*x^5 + 100*x^4 + 93*x^3 + 72*x^2 + 29*x + 86, x^75 + 41*x^73 + 66*x^72 + 82*x^71 + 72*x^70 + 74*x^69 + 60*x^68 + 21*x^67 + 104*x^66 + 117*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 18*x^7 + 72*x^6 + 10*x^5 + 60*x^4 + 61*x^3 + 104*x^2 + 93*x + 50, x^75 + 41*x^73 + 122*x^72 + 50*x^71 + 24*x^70 + 74*x^69 + 92*x^68 + 117*x^67 + 88*x^66 + 53*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 114*x^7 + 24*x^6 + 10*x^5 + 92*x^4 + 29*x^3 + 88*x^2 + 29*x + 26, x^75 + 41*x^73 + 50*x^72 + 98*x^71 + 88*x^70 + 26*x^69 + 44*x^68 + 69*x^67 + 24*x^66 + 101*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 34*x^7 + 88*x^6 + 90*x^5 + 44*x^4 + 109*x^3 + 24*x^2 + 77*x + 18, x^75 + 41*x^73 + 70*x^72 + 114*x^71 + 104*x^70 + 74*x^69 + 100*x^68 + 53*x^67 + 40*x^66 + 53*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 50*x^7 + 104*x^6 + 10*x^5 + 100*x^4 + 93*x^3 + 40*x^2 + 29*x + 102, x^75 + 41*x^73 + 34*x^72 + 114*x^71 + 104*x^70 + 106*x^69 + 28*x^68 + 117*x^67 + 72*x^66 + 85*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 50*x^7 + 104*x^6 + 42*x^5 + 28*x^4 + 29*x^3 + 72*x^2 + 61*x + 114, x^75 + 41*x^73 + 78*x^72 + 82*x^71 + 24*x^70 + 10*x^69 + 4*x^68 + 21*x^67 + 56*x^66 + 53*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 18*x^7 + 24*x^6 + 74*x^5 + 4*x^4 + 61*x^3 + 56*x^2 + 29*x + 126, x^75 + 41*x^73 + 66*x^72 + 18*x^71 + 104*x^70 + 74*x^69 + 28*x^68 + 85*x^67 + 72*x^66 + 117*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 82*x^7 + 104*x^6 + 10*x^5 + 28*x^4 + 125*x^3 + 72*x^2 + 93*x + 82, x^75 + 41*x^73 + 50*x^72 + 50*x^71 + 8*x^70 + 106*x^69 + 28*x^68 + 53*x^67 + 40*x^66 + 85*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 114*x^7 + 8*x^6 + 42*x^5 + 28*x^4 + 93*x^3 + 40*x^2 + 61*x + 98, x^75 + 41*x^73 + 10*x^72 + 82*x^71 + 56*x^70 + 106*x^69 + 28*x^68 + 85*x^67 + 56*x^66 + 21*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 18*x^7 + 56*x^6 + 42*x^5 + 28*x^4 + 125*x^3 + 56*x^2 + 125*x + 74, x^75 + 41*x^73 + 42*x^72 + 98*x^71 + 8*x^70 + 58*x^69 + 44*x^68 + 5*x^67 + 40*x^66 + 5*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 34*x^7 + 8*x^6 + 122*x^5 + 44*x^4 + 45*x^3 + 40*x^2 + 109*x + 90, x^75 + 41*x^73 + 30*x^72 + 50*x^71 + 56*x^70 + 106*x^69 + 68*x^68 + 53*x^67 + 24*x^66 + 85*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 114*x^7 + 56*x^6 + 42*x^5 + 68*x^4 + 93*x^3 + 24*x^2 + 61*x + 110, x^75 + 41*x^73 + 34*x^72 + 18*x^71 + 104*x^70 + 10*x^69 + 28*x^68 + 85*x^67 + 72*x^66 + 53*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 82*x^7 + 104*x^6 + 74*x^5 + 28*x^4 + 125*x^3 + 72*x^2 + 29*x + 114, x^75 + 41*x^73 + 62*x^72 + 82*x^71 + 88*x^70 + 74*x^69 + 100*x^68 + 21*x^67 + 120*x^66 + 117*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 18*x^7 + 88*x^6 + 10*x^5 + 100*x^4 + 61*x^3 + 120*x^2 + 93*x + 46, x^75 + 41*x^73 + 46*x^72 + 114*x^71 + 120*x^70 + 42*x^69 + 36*x^68 + 117*x^67 + 88*x^66 + 21*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 50*x^7 + 120*x^6 + 106*x^5 + 36*x^4 + 29*x^3 + 88*x^2 + 125*x + 126, x^75 + 41*x^73 + 50*x^72 + 82*x^71 + 8*x^70 + 10*x^69 + 28*x^68 + 21*x^67 + 40*x^66 + 53*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 18*x^7 + 8*x^6 + 74*x^5 + 28*x^4 + 61*x^3 + 40*x^2 + 29*x + 98, x^75 + 41*x^73 + 70*x^72 + 2*x^71 + 56*x^70 + 26*x^69 + 52*x^68 + 101*x^67 + 24*x^66 + 37*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 66*x^7 + 56*x^6 + 90*x^5 + 52*x^4 + 13*x^3 + 24*x^2 + 13*x + 86, x^75 + 41*x^73 + 54*x^72 + 2*x^71 + 120*x^70 + 26*x^69 + 84*x^68 + 101*x^67 + 88*x^66 + 37*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 66*x^7 + 120*x^6 + 90*x^5 + 84*x^4 + 13*x^3 + 88*x^2 + 13*x + 70, x^75 + 41*x^73 + 2*x^72 + 114*x^71 + 8*x^70 + 42*x^69 + 60*x^68 + 117*x^67 + 40*x^66 + 21*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 50*x^7 + 8*x^6 + 106*x^5 + 60*x^4 + 29*x^3 + 40*x^2 + 125*x + 114, x^75 + 41*x^73 + 98*x^72 + 114*x^71 + 104*x^70 + 106*x^69 + 28*x^68 + 117*x^67 + 72*x^66 + 85*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 50*x^7 + 104*x^6 + 42*x^5 + 28*x^4 + 29*x^3 + 72*x^2 + 61*x + 50, x^75 + 41*x^73 + 94*x^72 + 2*x^71 + 72*x^70 + 122*x^69 + 84*x^68 + 37*x^67 + 72*x^66 + 5*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 66*x^7 + 72*x^6 + 58*x^5 + 84*x^4 + 77*x^3 + 72*x^2 + 109*x + 94, x^75 + 41*x^73 + 90*x^72 + 66*x^71 + 104*x^70 + 90*x^69 + 44*x^68 + 37*x^67 + 72*x^66 + 101*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 2*x^7 + 104*x^6 + 26*x^5 + 44*x^4 + 77*x^3 + 72*x^2 + 77*x + 42, x^75 + 41*x^73 + 90*x^72 + 82*x^71 + 24*x^70 + 106*x^69 + 28*x^68 + 85*x^67 + 88*x^66 + 21*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 18*x^7 + 24*x^6 + 42*x^5 + 28*x^4 + 125*x^3 + 88*x^2 + 125*x + 122, x^75 + 41*x^73 + 66*x^72 + 66*x^71 + 24*x^70 + 58*x^69 + 76*x^68 + 101*x^67 + 88*x^66 + 69*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 2*x^7 + 24*x^6 + 122*x^5 + 76*x^4 + 13*x^3 + 88*x^2 + 45*x + 98, x^75 + 41*x^73 + 42*x^72 + 2*x^71 + 104*x^70 + 26*x^69 + 76*x^68 + 101*x^67 + 72*x^66 + 37*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 66*x^7 + 104*x^6 + 90*x^5 + 76*x^4 + 13*x^3 + 72*x^2 + 13*x + 58, x^75 + 41*x^73 + 42*x^72 + 98*x^71 + 104*x^70 + 122*x^69 + 76*x^68 + 5*x^67 + 72*x^66 + 69*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 34*x^7 + 104*x^6 + 58*x^5 + 76*x^4 + 45*x^3 + 72*x^2 + 45*x + 58, x^75 + 41*x^73 + 94*x^72 + 66*x^71 + 72*x^70 + 122*x^69 + 20*x^68 + 101*x^67 + 72*x^66 + 5*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 2*x^7 + 72*x^6 + 58*x^5 + 20*x^4 + 13*x^3 + 72*x^2 + 109*x + 30, x^75 + 41*x^73 + 34*x^72 + 18*x^71 + 72*x^70 + 74*x^69 + 60*x^68 + 85*x^67 + 104*x^66 + 117*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 82*x^7 + 72*x^6 + 10*x^5 + 60*x^4 + 125*x^3 + 104*x^2 + 93*x + 82, x^75 + 41*x^73 + 78*x^72 + 98*x^71 + 104*x^70 + 90*x^69 + 84*x^68 + 69*x^67 + 40*x^66 + 37*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 34*x^7 + 104*x^6 + 26*x^5 + 84*x^4 + 109*x^3 + 40*x^2 + 13*x + 110, x^75 + 41*x^73 + 6*x^72 + 82*x^71 + 104*x^70 + 42*x^69 + 100*x^68 + 85*x^67 + 40*x^66 + 85*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 18*x^7 + 104*x^6 + 106*x^5 + 100*x^4 + 125*x^3 + 40*x^2 + 61*x + 38, x^75 + 41*x^73 + 110*x^72 + 2*x^71 + 72*x^70 + 122*x^69 + 116*x^68 + 37*x^67 + 72*x^66 + 5*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 66*x^7 + 72*x^6 + 58*x^5 + 116*x^4 + 77*x^3 + 72*x^2 + 109*x + 46, x^75 + 41*x^73 + 42*x^72 + 82*x^71 + 24*x^70 + 42*x^69 + 124*x^68 + 85*x^67 + 88*x^66 + 85*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 18*x^7 + 24*x^6 + 106*x^5 + 124*x^4 + 125*x^3 + 88*x^2 + 61*x + 74, x^75 + 41*x^73 + 122*x^72 + 34*x^71 + 8*x^70 + 58*x^69 + 12*x^68 + 69*x^67 + 40*x^66 + 5*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 98*x^7 + 8*x^6 + 122*x^5 + 12*x^4 + 109*x^3 + 40*x^2 + 109*x + 42, x^75 + 41*x^73 + 58*x^72 + 66*x^71 + 72*x^70 + 26*x^69 + 12*x^68 + 37*x^67 + 104*x^66 + 37*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 2*x^7 + 72*x^6 + 90*x^5 + 12*x^4 + 77*x^3 + 104*x^2 + 13*x + 106, x^75 + 41*x^73 + 54*x^72 + 18*x^71 + 8*x^70 + 42*x^69 + 36*x^68 + 21*x^67 + 8*x^66 + 85*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 82*x^7 + 8*x^6 + 106*x^5 + 36*x^4 + 61*x^3 + 8*x^2 + 61*x + 54, x^75 + 41*x^73 + 30*x^72 + 114*x^71 + 120*x^70 + 42*x^69 + 4*x^68 + 117*x^67 + 88*x^66 + 21*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 50*x^7 + 120*x^6 + 106*x^5 + 4*x^4 + 29*x^3 + 88*x^2 + 125*x + 46, x^75 + 41*x^73 + 74*x^72 + 2*x^71 + 104*x^70 + 26*x^69 + 12*x^68 + 101*x^67 + 72*x^66 + 37*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 66*x^7 + 104*x^6 + 90*x^5 + 12*x^4 + 13*x^3 + 72*x^2 + 13*x + 90, x^75 + 41*x^73 + 62*x^72 + 2*x^71 + 8*x^70 + 122*x^69 + 84*x^68 + 37*x^67 + 8*x^66 + 5*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 66*x^7 + 8*x^6 + 58*x^5 + 84*x^4 + 77*x^3 + 8*x^2 + 109*x + 126, x^75 + 41*x^73 + 30*x^72 + 66*x^71 + 104*x^70 + 122*x^69 + 52*x^68 + 101*x^67 + 40*x^66 + 5*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 2*x^7 + 104*x^6 + 58*x^5 + 52*x^4 + 13*x^3 + 40*x^2 + 109*x + 62, x^75 + 41*x^73 + 102*x^72 + 114*x^71 + 8*x^70 + 10*x^69 + 4*x^68 + 53*x^67 + 8*x^66 + 117*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 50*x^7 + 8*x^6 + 74*x^5 + 4*x^4 + 93*x^3 + 8*x^2 + 93*x + 38, x^75 + 41*x^73 + 78*x^72 + 66*x^71 + 104*x^70 + 122*x^69 + 20*x^68 + 101*x^67 + 40*x^66 + 5*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 2*x^7 + 104*x^6 + 58*x^5 + 20*x^4 + 13*x^3 + 40*x^2 + 109*x + 46, x^75 + 41*x^73 + 122*x^72 + 114*x^71 + 24*x^70 + 10*x^69 + 92*x^68 + 53*x^67 + 88*x^66 + 117*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 50*x^7 + 24*x^6 + 74*x^5 + 92*x^4 + 93*x^3 + 88*x^2 + 93*x + 26, x^75 + 41*x^73 + 90*x^72 + 66*x^71 + 104*x^70 + 26*x^69 + 108*x^68 + 37*x^67 + 72*x^66 + 37*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 2*x^7 + 104*x^6 + 90*x^5 + 108*x^4 + 77*x^3 + 72*x^2 + 13*x + 106, x^75 + 41*x^73 + 54*x^72 + 98*x^71 + 120*x^70 + 58*x^69 + 20*x^68 + 5*x^67 + 88*x^66 + 5*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 34*x^7 + 120*x^6 + 122*x^5 + 20*x^4 + 45*x^3 + 88*x^2 + 109*x + 6, x^75 + 41*x^73 + 6*x^72 + 66*x^71 + 24*x^70 + 90*x^69 + 20*x^68 + 37*x^67 + 56*x^66 + 101*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 2*x^7 + 24*x^6 + 26*x^5 + 20*x^4 + 77*x^3 + 56*x^2 + 77*x + 54, x^75 + 41*x^73 + 30*x^72 + 98*x^71 + 40*x^70 + 90*x^69 + 52*x^68 + 69*x^67 + 104*x^66 + 37*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 34*x^7 + 40*x^6 + 26*x^5 + 52*x^4 + 109*x^3 + 104*x^2 + 13*x + 62, x^75 + 41*x^73 + 54*x^72 + 34*x^71 + 88*x^70 + 122*x^69 + 116*x^68 + 69*x^67 + 120*x^66 + 69*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 98*x^7 + 88*x^6 + 58*x^5 + 116*x^4 + 109*x^3 + 120*x^2 + 45*x + 38, x^75 + 41*x^73 + 78*x^72 + 66*x^71 + 8*x^70 + 122*x^69 + 52*x^68 + 101*x^67 + 8*x^66 + 5*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 2*x^7 + 8*x^6 + 58*x^5 + 52*x^4 + 13*x^3 + 8*x^2 + 109*x + 14, x^75 + 41*x^73 + 58*x^72 + 34*x^71 + 72*x^70 + 58*x^69 + 76*x^68 + 69*x^67 + 104*x^66 + 5*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 98*x^7 + 72*x^6 + 122*x^5 + 76*x^4 + 109*x^3 + 104*x^2 + 109*x + 42, x^75 + 41*x^73 + 22*x^72 + 2*x^71 + 120*x^70 + 26*x^69 + 20*x^68 + 101*x^67 + 88*x^66 + 37*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 66*x^7 + 120*x^6 + 90*x^5 + 20*x^4 + 13*x^3 + 88*x^2 + 13*x + 38, x^75 + 41*x^73 + 10*x^72 + 66*x^71 + 104*x^70 + 90*x^69 + 12*x^68 + 37*x^67 + 72*x^66 + 101*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 2*x^7 + 104*x^6 + 26*x^5 + 12*x^4 + 77*x^3 + 72*x^2 + 77*x + 26, x^75 + 41*x^73 + 26*x^72 + 18*x^71 + 88*x^70 + 42*x^69 + 92*x^68 + 21*x^67 + 24*x^66 + 85*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 82*x^7 + 88*x^6 + 106*x^5 + 92*x^4 + 61*x^3 + 24*x^2 + 61*x + 122, x^75 + 41*x^73 + 58*x^72 + 114*x^71 + 88*x^70 + 10*x^69 + 28*x^68 + 53*x^67 + 24*x^66 + 117*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 50*x^7 + 88*x^6 + 74*x^5 + 28*x^4 + 93*x^3 + 24*x^2 + 93*x + 26, x^75 + 41*x^73 + 38*x^72 + 66*x^71 + 120*x^70 + 90*x^69 + 52*x^68 + 37*x^67 + 88*x^66 + 101*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 2*x^7 + 120*x^6 + 26*x^5 + 52*x^4 + 77*x^3 + 88*x^2 + 77*x + 118, x^75 + 41*x^73 + 38*x^72 + 98*x^71 + 120*x^70 + 122*x^69 + 52*x^68 + 5*x^67 + 88*x^66 + 69*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 34*x^7 + 120*x^6 + 58*x^5 + 52*x^4 + 45*x^3 + 88*x^2 + 45*x + 118, x^75 + 41*x^73 + 42*x^72 + 50*x^71 + 120*x^70 + 10*x^69 + 92*x^68 + 117*x^67 + 120*x^66 + 117*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 114*x^7 + 120*x^6 + 74*x^5 + 92*x^4 + 29*x^3 + 120*x^2 + 93*x + 106, x^75 + 41*x^73 + 94*x^72 + 82*x^71 + 88*x^70 + 10*x^69 + 100*x^68 + 21*x^67 + 120*x^66 + 53*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 18*x^7 + 88*x^6 + 74*x^5 + 100*x^4 + 61*x^3 + 120*x^2 + 29*x + 14, x^75 + 41*x^73 + 2*x^72 + 34*x^71 + 56*x^70 + 26*x^69 + 108*x^68 + 5*x^67 + 56*x^66 + 101*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 98*x^7 + 56*x^6 + 90*x^5 + 108*x^4 + 45*x^3 + 56*x^2 + 77*x + 2, x^75 + 41*x^73 + 82*x^72 + 98*x^71 + 56*x^70 + 90*x^69 + 12*x^68 + 69*x^67 + 56*x^66 + 37*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 34*x^7 + 56*x^6 + 26*x^5 + 12*x^4 + 109*x^3 + 56*x^2 + 13*x + 18, x^75 + 41*x^73 + 102*x^72 + 114*x^71 + 72*x^70 + 74*x^69 + 4*x^68 + 53*x^67 + 72*x^66 + 53*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 50*x^7 + 72*x^6 + 10*x^5 + 4*x^4 + 93*x^3 + 72*x^2 + 29*x + 38, x^75 + 41*x^73 + 18*x^72 + 50*x^71 + 72*x^70 + 42*x^69 + 92*x^68 + 53*x^67 + 104*x^66 + 21*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 114*x^7 + 72*x^6 + 106*x^5 + 92*x^4 + 93*x^3 + 104*x^2 + 125*x + 66, x^75 + 41*x^73 + 6*x^72 + 98*x^71 + 56*x^70 + 58*x^69 + 116*x^68 + 5*x^67 + 24*x^66 + 5*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 34*x^7 + 56*x^6 + 122*x^5 + 116*x^4 + 45*x^3 + 24*x^2 + 109*x + 86, x^75 + 41*x^73 + 70*x^72 + 34*x^71 + 120*x^70 + 58*x^69 + 116*x^68 + 69*x^67 + 88*x^66 + 5*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 98*x^7 + 120*x^6 + 122*x^5 + 116*x^4 + 109*x^3 + 88*x^2 + 109*x + 22, x^75 + 41*x^73 + 54*x^72 + 18*x^71 + 72*x^70 + 106*x^69 + 36*x^68 + 21*x^67 + 72*x^66 + 21*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 82*x^7 + 72*x^6 + 42*x^5 + 36*x^4 + 61*x^3 + 72*x^2 + 125*x + 54, x^75 + 41*x^73 + 10*x^72 + 2*x^71 + 8*x^70 + 90*x^69 + 108*x^68 + 101*x^67 + 40*x^66 + 101*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 66*x^7 + 8*x^6 + 26*x^5 + 108*x^4 + 13*x^3 + 40*x^2 + 77*x + 58, x^75 + 41*x^73 + 66*x^72 + 50*x^71 + 104*x^70 + 42*x^69 + 92*x^68 + 53*x^67 + 72*x^66 + 21*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 114*x^7 + 104*x^6 + 106*x^5 + 92*x^4 + 93*x^3 + 72*x^2 + 125*x + 18, x^75 + 41*x^73 + 110*x^72 + 34*x^71 + 72*x^70 + 90*x^69 + 52*x^68 + 5*x^67 + 72*x^66 + 37*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 98*x^7 + 72*x^6 + 26*x^5 + 52*x^4 + 45*x^3 + 72*x^2 + 13*x + 110, x^75 + 41*x^73 + 54*x^72 + 50*x^71 + 8*x^70 + 10*x^69 + 100*x^68 + 117*x^67 + 8*x^66 + 117*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 114*x^7 + 8*x^6 + 74*x^5 + 100*x^4 + 29*x^3 + 8*x^2 + 93*x + 118, x^75 + 41*x^73 + 26*x^72 + 2*x^71 + 72*x^70 + 26*x^69 + 12*x^68 + 101*x^67 + 104*x^66 + 37*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 66*x^7 + 72*x^6 + 90*x^5 + 12*x^4 + 13*x^3 + 104*x^2 + 13*x + 10, x^75 + 41*x^73 + 70*x^72 + 50*x^71 + 104*x^70 + 10*x^69 + 100*x^68 + 117*x^67 + 40*x^66 + 117*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 114*x^7 + 104*x^6 + 74*x^5 + 100*x^4 + 29*x^3 + 40*x^2 + 93*x + 102, x^75 + 41*x^73 + 42*x^72 + 18*x^71 + 24*x^70 + 42*x^69 + 60*x^68 + 21*x^67 + 88*x^66 + 85*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 82*x^7 + 24*x^6 + 106*x^5 + 60*x^4 + 61*x^3 + 88*x^2 + 61*x + 10, x^75 + 41*x^73 + 14*x^72 + 50*x^71 + 88*x^70 + 42*x^69 + 4*x^68 + 53*x^67 + 120*x^66 + 21*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 114*x^7 + 88*x^6 + 106*x^5 + 4*x^4 + 93*x^3 + 120*x^2 + 125*x + 62, x^75 + 41*x^73 + 38*x^72 + 50*x^71 + 104*x^70 + 10*x^69 + 36*x^68 + 117*x^67 + 40*x^66 + 117*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 114*x^7 + 104*x^6 + 74*x^5 + 36*x^4 + 29*x^3 + 40*x^2 + 93*x + 70, x^75 + 41*x^73 + 126*x^72 + 98*x^71 + 72*x^70 + 26*x^69 + 84*x^68 + 69*x^67 + 72*x^66 + 101*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 34*x^7 + 72*x^6 + 90*x^5 + 84*x^4 + 109*x^3 + 72*x^2 + 77*x + 62, x^75 + 41*x^73 + 118*x^72 + 2*x^71 + 56*x^70 + 26*x^69 + 20*x^68 + 101*x^67 + 24*x^66 + 37*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 66*x^7 + 56*x^6 + 90*x^5 + 20*x^4 + 13*x^3 + 24*x^2 + 13*x + 70, x^75 + 41*x^73 + 46*x^72 + 34*x^71 + 40*x^70 + 90*x^69 + 20*x^68 + 5*x^67 + 104*x^66 + 37*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 98*x^7 + 40*x^6 + 26*x^5 + 20*x^4 + 45*x^3 + 104*x^2 + 13*x + 78, x^75 + 41*x^73 + 110*x^72 + 34*x^71 + 40*x^70 + 90*x^69 + 20*x^68 + 5*x^67 + 104*x^66 + 37*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 98*x^7 + 40*x^6 + 26*x^5 + 20*x^4 + 45*x^3 + 104*x^2 + 13*x + 14, x^75 + 41*x^73 + 106*x^72 + 2*x^71 + 72*x^70 + 90*x^69 + 108*x^68 + 101*x^67 + 104*x^66 + 101*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 66*x^7 + 72*x^6 + 26*x^5 + 108*x^4 + 13*x^3 + 104*x^2 + 77*x + 90, x^75 + 41*x^73 + 94*x^72 + 18*x^71 + 88*x^70 + 10*x^69 + 36*x^68 + 85*x^67 + 120*x^66 + 53*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 82*x^7 + 88*x^6 + 74*x^5 + 36*x^4 + 125*x^3 + 120*x^2 + 29*x + 78, x^75 + 41*x^73 + 38*x^72 + 34*x^71 + 56*x^70 + 122*x^69 + 52*x^68 + 69*x^67 + 24*x^66 + 69*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 98*x^7 + 56*x^6 + 58*x^5 + 52*x^4 + 109*x^3 + 24*x^2 + 45*x + 118, x^75 + 41*x^73 + 106*x^72 + 82*x^71 + 88*x^70 + 42*x^69 + 60*x^68 + 85*x^67 + 24*x^66 + 85*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 18*x^7 + 88*x^6 + 106*x^5 + 60*x^4 + 125*x^3 + 24*x^2 + 61*x + 74, x^75 + 41*x^73 + 46*x^72 + 2*x^71 + 104*x^70 + 122*x^69 + 20*x^68 + 37*x^67 + 40*x^66 + 5*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 66*x^7 + 104*x^6 + 58*x^5 + 20*x^4 + 77*x^3 + 40*x^2 + 109*x + 78, x^75 + 41*x^73 + 10*x^72 + 34*x^71 + 72*x^70 + 122*x^69 + 44*x^68 + 69*x^67 + 104*x^66 + 69*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 98*x^7 + 72*x^6 + 58*x^5 + 44*x^4 + 109*x^3 + 104*x^2 + 45*x + 122, x^75 + 41*x^73 + 98*x^72 + 18*x^71 + 40*x^70 + 10*x^69 + 92*x^68 + 85*x^67 + 8*x^66 + 53*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 82*x^7 + 40*x^6 + 74*x^5 + 92*x^4 + 125*x^3 + 8*x^2 + 29*x + 114, x^75 + 41*x^73 + 98*x^72 + 98*x^71 + 56*x^70 + 90*x^69 + 44*x^68 + 69*x^67 + 56*x^66 + 37*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 34*x^7 + 56*x^6 + 26*x^5 + 44*x^4 + 109*x^3 + 56*x^2 + 13*x + 98, x^75 + 41*x^73 + 54*x^72 + 50*x^71 + 72*x^70 + 74*x^69 + 100*x^68 + 117*x^67 + 72*x^66 + 53*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 114*x^7 + 72*x^6 + 10*x^5 + 100*x^4 + 29*x^3 + 72*x^2 + 29*x + 118, x^75 + 41*x^73 + 42*x^72 + 34*x^71 + 40*x^70 + 58*x^69 + 12*x^68 + 69*x^67 + 8*x^66 + 5*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 98*x^7 + 40*x^6 + 122*x^5 + 12*x^4 + 109*x^3 + 8*x^2 + 109*x + 122, x^75 + 41*x^73 + 26*x^72 + 66*x^71 + 40*x^70 + 90*x^69 + 108*x^68 + 37*x^67 + 8*x^66 + 101*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 2*x^7 + 40*x^6 + 26*x^5 + 108*x^4 + 77*x^3 + 8*x^2 + 77*x + 42, x^75 + 41*x^73 + 66*x^72 + 34*x^71 + 24*x^70 + 26*x^69 + 76*x^68 + 5*x^67 + 88*x^66 + 101*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 98*x^7 + 24*x^6 + 90*x^5 + 76*x^4 + 45*x^3 + 88*x^2 + 77*x + 98, x^75 + 41*x^73 + 74*x^72 + 98*x^71 + 8*x^70 + 122*x^69 + 44*x^68 + 5*x^67 + 40*x^66 + 69*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 34*x^7 + 8*x^6 + 58*x^5 + 44*x^4 + 45*x^3 + 40*x^2 + 45*x + 58, x^75 + 41*x^73 + 10*x^72 + 18*x^71 + 120*x^70 + 106*x^69 + 28*x^68 + 21*x^67 + 120*x^66 + 21*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 82*x^7 + 120*x^6 + 42*x^5 + 28*x^4 + 61*x^3 + 120*x^2 + 125*x + 74, x^75 + 41*x^73 + 110*x^72 + 98*x^71 + 8*x^70 + 90*x^69 + 52*x^68 + 69*x^67 + 8*x^66 + 37*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 34*x^7 + 8*x^6 + 26*x^5 + 52*x^4 + 109*x^3 + 8*x^2 + 13*x + 110, x^75 + 41*x^73 + 110*x^72 + 82*x^71 + 56*x^70 + 10*x^69 + 100*x^68 + 21*x^67 + 24*x^66 + 53*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 18*x^7 + 56*x^6 + 74*x^5 + 100*x^4 + 61*x^3 + 24*x^2 + 29*x + 126, x^75 + 41*x^73 + 34*x^72 + 34*x^71 + 88*x^70 + 90*x^69 + 12*x^68 + 5*x^67 + 24*x^66 + 37*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 98*x^7 + 88*x^6 + 26*x^5 + 12*x^4 + 45*x^3 + 24*x^2 + 13*x + 66, x^75 + 41*x^73 + 94*x^72 + 66*x^71 + 8*x^70 + 122*x^69 + 84*x^68 + 101*x^67 + 8*x^66 + 5*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 2*x^7 + 8*x^6 + 58*x^5 + 84*x^4 + 13*x^3 + 8*x^2 + 109*x + 94, x^75 + 41*x^73 + 70*x^72 + 34*x^71 + 88*x^70 + 58*x^69 + 84*x^68 + 69*x^67 + 120*x^66 + 5*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 98*x^7 + 88*x^6 + 122*x^5 + 84*x^4 + 109*x^3 + 120*x^2 + 109*x + 54, x^75 + 41*x^73 + 50*x^72 + 2*x^71 + 88*x^70 + 58*x^69 + 44*x^68 + 37*x^67 + 24*x^66 + 69*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 66*x^7 + 88*x^6 + 122*x^5 + 44*x^4 + 77*x^3 + 24*x^2 + 45*x + 18, x^75 + 41*x^73 + 82*x^72 + 114*x^71 + 40*x^70 + 106*x^69 + 60*x^68 + 117*x^67 + 8*x^66 + 85*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 50*x^7 + 40*x^6 + 42*x^5 + 60*x^4 + 29*x^3 + 8*x^2 + 61*x + 34, x^75 + 41*x^73 + 26*x^72 + 50*x^71 + 24*x^70 + 74*x^69 + 28*x^68 + 117*x^67 + 88*x^66 + 53*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 114*x^7 + 24*x^6 + 10*x^5 + 28*x^4 + 29*x^3 + 88*x^2 + 29*x + 58, x^75 + 41*x^73 + 22*x^72 + 2*x^71 + 88*x^70 + 26*x^69 + 116*x^68 + 101*x^67 + 120*x^66 + 37*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 66*x^7 + 88*x^6 + 90*x^5 + 116*x^4 + 13*x^3 + 120*x^2 + 13*x + 70, x^75 + 41*x^73 + 94*x^72 + 50*x^71 + 120*x^70 + 42*x^69 + 68*x^68 + 53*x^67 + 88*x^66 + 21*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 114*x^7 + 120*x^6 + 106*x^5 + 68*x^4 + 93*x^3 + 88*x^2 + 125*x + 46, x^75 + 41*x^73 + 66*x^72 + 114*x^71 + 72*x^70 + 106*x^69 + 60*x^68 + 117*x^67 + 104*x^66 + 85*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 50*x^7 + 72*x^6 + 42*x^5 + 60*x^4 + 29*x^3 + 104*x^2 + 61*x + 50, x^75 + 41*x^73 + 110*x^72 + 66*x^71 + 8*x^70 + 122*x^69 + 116*x^68 + 101*x^67 + 8*x^66 + 5*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 2*x^7 + 8*x^6 + 58*x^5 + 116*x^4 + 13*x^3 + 8*x^2 + 109*x + 46, x^75 + 41*x^73 + 14*x^72 + 82*x^71 + 24*x^70 + 10*x^69 + 4*x^68 + 21*x^67 + 56*x^66 + 53*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 18*x^7 + 24*x^6 + 74*x^5 + 4*x^4 + 61*x^3 + 56*x^2 + 29*x + 62, x^75 + 41*x^73 + 98*x^72 + 114*x^71 + 72*x^70 + 42*x^69 + 60*x^68 + 117*x^67 + 104*x^66 + 21*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 50*x^7 + 72*x^6 + 106*x^5 + 60*x^4 + 29*x^3 + 104*x^2 + 125*x + 18, x^75 + 41*x^73 + 86*x^72 + 2*x^71 + 24*x^70 + 26*x^69 + 52*x^68 + 101*x^67 + 56*x^66 + 37*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 66*x^7 + 24*x^6 + 90*x^5 + 52*x^4 + 13*x^3 + 56*x^2 + 13*x + 70, x^75 + 41*x^73 + 54*x^72 + 2*x^71 + 88*x^70 + 26*x^69 + 52*x^68 + 101*x^67 + 120*x^66 + 37*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 66*x^7 + 88*x^6 + 90*x^5 + 52*x^4 + 13*x^3 + 120*x^2 + 13*x + 102, x^75 + 41*x^73 + 118*x^72 + 98*x^71 + 120*x^70 + 122*x^69 + 84*x^68 + 5*x^67 + 88*x^66 + 69*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 34*x^7 + 120*x^6 + 58*x^5 + 84*x^4 + 45*x^3 + 88*x^2 + 45*x + 6, x^75 + 41*x^73 + 54*x^72 + 18*x^71 + 40*x^70 + 106*x^69 + 4*x^68 + 21*x^67 + 104*x^66 + 21*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 82*x^7 + 40*x^6 + 42*x^5 + 4*x^4 + 61*x^3 + 104*x^2 + 125*x + 86, x^75 + 41*x^73 + 22*x^72 + 82*x^71 + 40*x^70 + 42*x^69 + 68*x^68 + 85*x^67 + 104*x^66 + 85*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 18*x^7 + 40*x^6 + 106*x^5 + 68*x^4 + 125*x^3 + 104*x^2 + 61*x + 54, x^75 + 41*x^73 + 30*x^72 + 34*x^71 + 72*x^70 + 90*x^69 + 20*x^68 + 5*x^67 + 72*x^66 + 37*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 98*x^7 + 72*x^6 + 26*x^5 + 20*x^4 + 45*x^3 + 72*x^2 + 13*x + 94, x^75 + 41*x^73 + 58*x^72 + 2*x^71 + 40*x^70 + 26*x^69 + 44*x^68 + 101*x^67 + 8*x^66 + 37*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 66*x^7 + 40*x^6 + 90*x^5 + 44*x^4 + 13*x^3 + 8*x^2 + 13*x + 74, x^75 + 41*x^73 + 74*x^72 + 82*x^71 + 88*x^70 + 106*x^69 + 60*x^68 + 85*x^67 + 24*x^66 + 21*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 18*x^7 + 88*x^6 + 42*x^5 + 60*x^4 + 125*x^3 + 24*x^2 + 125*x + 106, x^75 + 41*x^73 + 2*x^72 + 34*x^71 + 24*x^70 + 90*x^69 + 12*x^68 + 5*x^67 + 88*x^66 + 37*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 98*x^7 + 24*x^6 + 26*x^5 + 12*x^4 + 45*x^3 + 88*x^2 + 13*x + 98, x^75 + 41*x^73 + 54*x^72 + 66*x^71 + 24*x^70 + 90*x^69 + 116*x^68 + 37*x^67 + 56*x^66 + 101*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 2*x^7 + 24*x^6 + 26*x^5 + 116*x^4 + 77*x^3 + 56*x^2 + 77*x + 38, x^75 + 41*x^73 + 38*x^72 + 2*x^71 + 56*x^70 + 26*x^69 + 116*x^68 + 101*x^67 + 24*x^66 + 37*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 66*x^7 + 56*x^6 + 90*x^5 + 116*x^4 + 13*x^3 + 24*x^2 + 13*x + 54, x^75 + 41*x^73 + 86*x^72 + 114*x^71 + 72*x^70 + 10*x^69 + 36*x^68 + 53*x^67 + 72*x^66 + 117*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 50*x^7 + 72*x^6 + 74*x^5 + 36*x^4 + 93*x^3 + 72*x^2 + 93*x + 22, x^75 + 41*x^73 + 50*x^72 + 82*x^71 + 72*x^70 + 74*x^69 + 28*x^68 + 21*x^67 + 104*x^66 + 117*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 18*x^7 + 72*x^6 + 10*x^5 + 28*x^4 + 61*x^3 + 104*x^2 + 93*x + 98, x^75 + 41*x^73 + 42*x^72 + 50*x^71 + 120*x^70 + 74*x^69 + 28*x^68 + 117*x^67 + 120*x^66 + 53*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 114*x^7 + 120*x^6 + 10*x^5 + 28*x^4 + 29*x^3 + 120*x^2 + 29*x + 42, x^75 + 41*x^73 + 18*x^72 + 98*x^71 + 120*x^70 + 26*x^69 + 12*x^68 + 69*x^67 + 120*x^66 + 101*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 34*x^7 + 120*x^6 + 90*x^5 + 12*x^4 + 109*x^3 + 120*x^2 + 77*x + 82, x^75 + 41*x^73 + 102*x^72 + 98*x^71 + 56*x^70 + 58*x^69 + 52*x^68 + 5*x^67 + 24*x^66 + 5*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 34*x^7 + 56*x^6 + 122*x^5 + 52*x^4 + 45*x^3 + 24*x^2 + 109*x + 54, x^75 + 41*x^73 + 38*x^72 + 34*x^71 + 24*x^70 + 122*x^69 + 20*x^68 + 69*x^67 + 56*x^66 + 69*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 98*x^7 + 24*x^6 + 58*x^5 + 20*x^4 + 109*x^3 + 56*x^2 + 45*x + 22, x^75 + 41*x^73 + 66*x^72 + 98*x^71 + 24*x^70 + 26*x^69 + 12*x^68 + 69*x^67 + 88*x^66 + 101*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 34*x^7 + 24*x^6 + 90*x^5 + 12*x^4 + 109*x^3 + 88*x^2 + 77*x + 34, x^75 + 41*x^73 + 14*x^72 + 82*x^71 + 88*x^70 + 74*x^69 + 4*x^68 + 21*x^67 + 120*x^66 + 117*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 18*x^7 + 88*x^6 + 10*x^5 + 4*x^4 + 61*x^3 + 120*x^2 + 93*x + 62, x^75 + 41*x^73 + 46*x^72 + 98*x^71 + 104*x^70 + 90*x^69 + 20*x^68 + 69*x^67 + 40*x^66 + 37*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 34*x^7 + 104*x^6 + 26*x^5 + 20*x^4 + 109*x^3 + 40*x^2 + 13*x + 78, x^75 + 41*x^73 + 22*x^72 + 114*x^71 + 72*x^70 + 74*x^69 + 100*x^68 + 53*x^67 + 72*x^66 + 53*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 50*x^7 + 72*x^6 + 10*x^5 + 100*x^4 + 93*x^3 + 72*x^2 + 29*x + 22, x^75 + 41*x^73 + 82*x^72 + 2*x^71 + 24*x^70 + 122*x^69 + 108*x^68 + 37*x^67 + 88*x^66 + 5*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 66*x^7 + 24*x^6 + 58*x^5 + 108*x^4 + 77*x^3 + 88*x^2 + 109*x + 50, x^75 + 41*x^73 + 98*x^72 + 114*x^71 + 40*x^70 + 42*x^69 + 28*x^68 + 117*x^67 + 8*x^66 + 21*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 50*x^7 + 40*x^6 + 106*x^5 + 28*x^4 + 29*x^3 + 8*x^2 + 125*x + 50, x^75 + 41*x^73 + 34*x^72 + 82*x^71 + 8*x^70 + 10*x^69 + 124*x^68 + 21*x^67 + 40*x^66 + 53*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 18*x^7 + 8*x^6 + 74*x^5 + 124*x^4 + 61*x^3 + 40*x^2 + 29*x + 18, x^75 + 41*x^73 + 118*x^72 + 82*x^71 + 8*x^70 + 42*x^69 + 100*x^68 + 85*x^67 + 8*x^66 + 85*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 18*x^7 + 8*x^6 + 106*x^5 + 100*x^4 + 125*x^3 + 8*x^2 + 61*x + 54, x^75 + 41*x^73 + 86*x^72 + 66*x^71 + 88*x^70 + 26*x^69 + 52*x^68 + 37*x^67 + 120*x^66 + 37*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 2*x^7 + 88*x^6 + 90*x^5 + 52*x^4 + 77*x^3 + 120*x^2 + 13*x + 70, x^75 + 41*x^73 + 122*x^72 + 66*x^71 + 104*x^70 + 90*x^69 + 108*x^68 + 37*x^67 + 72*x^66 + 101*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 2*x^7 + 104*x^6 + 26*x^5 + 108*x^4 + 77*x^3 + 72*x^2 + 77*x + 74, x^75 + 41*x^73 + 110*x^72 + 114*x^71 + 24*x^70 + 106*x^69 + 4*x^68 + 117*x^67 + 56*x^66 + 85*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 50*x^7 + 24*x^6 + 42*x^5 + 4*x^4 + 29*x^3 + 56*x^2 + 61*x + 94, x^75 + 41*x^73 + 114*x^72 + 18*x^71 + 40*x^70 + 74*x^69 + 60*x^68 + 85*x^67 + 8*x^66 + 117*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 82*x^7 + 40*x^6 + 10*x^5 + 60*x^4 + 125*x^3 + 8*x^2 + 93*x + 2, x^75 + 41*x^73 + 14*x^72 + 34*x^71 + 104*x^70 + 26*x^69 + 84*x^68 + 5*x^67 + 40*x^66 + 101*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 98*x^7 + 104*x^6 + 90*x^5 + 84*x^4 + 45*x^3 + 40*x^2 + 77*x + 46, x^75 + 41*x^73 + 54*x^72 + 50*x^71 + 8*x^70 + 74*x^69 + 36*x^68 + 117*x^67 + 8*x^66 + 53*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 114*x^7 + 8*x^6 + 10*x^5 + 36*x^4 + 29*x^3 + 8*x^2 + 29*x + 54, x^75 + 41*x^73 + 30*x^72 + 98*x^71 + 8*x^70 + 90*x^69 + 20*x^68 + 69*x^67 + 8*x^66 + 37*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 34*x^7 + 8*x^6 + 26*x^5 + 20*x^4 + 109*x^3 + 8*x^2 + 13*x + 94, x^75 + 41*x^73 + 90*x^72 + 34*x^71 + 8*x^70 + 58*x^69 + 76*x^68 + 69*x^67 + 40*x^66 + 5*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 98*x^7 + 8*x^6 + 122*x^5 + 76*x^4 + 109*x^3 + 40*x^2 + 109*x + 10, x^75 + 41*x^73 + 122*x^72 + 82*x^71 + 24*x^70 + 106*x^69 + 92*x^68 + 85*x^67 + 88*x^66 + 21*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 18*x^7 + 24*x^6 + 42*x^5 + 92*x^4 + 125*x^3 + 88*x^2 + 125*x + 26, x^75 + 41*x^73 + 30*x^72 + 66*x^71 + 8*x^70 + 58*x^69 + 20*x^68 + 101*x^67 + 8*x^66 + 69*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 2*x^7 + 8*x^6 + 122*x^5 + 20*x^4 + 13*x^3 + 8*x^2 + 45*x + 94, x^75 + 41*x^73 + 74*x^72 + 66*x^71 + 72*x^70 + 26*x^69 + 44*x^68 + 37*x^67 + 104*x^66 + 37*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 2*x^7 + 72*x^6 + 90*x^5 + 44*x^4 + 77*x^3 + 104*x^2 + 13*x + 58, x^75 + 41*x^73 + 58*x^72 + 98*x^71 + 8*x^70 + 58*x^69 + 76*x^68 + 5*x^67 + 40*x^66 + 5*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 34*x^7 + 8*x^6 + 122*x^5 + 76*x^4 + 45*x^3 + 40*x^2 + 109*x + 42, x^75 + 41*x^73 + 66*x^72 + 18*x^71 + 40*x^70 + 10*x^69 + 28*x^68 + 85*x^67 + 8*x^66 + 53*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 82*x^7 + 40*x^6 + 74*x^5 + 28*x^4 + 125*x^3 + 8*x^2 + 29*x + 82, x^75 + 41*x^73 + 54*x^72 + 2*x^71 + 56*x^70 + 26*x^69 + 20*x^68 + 101*x^67 + 24*x^66 + 37*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 66*x^7 + 56*x^6 + 90*x^5 + 20*x^4 + 13*x^3 + 24*x^2 + 13*x + 6, x^75 + 41*x^73 + 126*x^72 + 18*x^71 + 88*x^70 + 10*x^69 + 100*x^68 + 85*x^67 + 120*x^66 + 53*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 82*x^7 + 88*x^6 + 74*x^5 + 100*x^4 + 125*x^3 + 120*x^2 + 29*x + 110, x^75 + 41*x^73 + 70*x^72 + 18*x^71 + 104*x^70 + 106*x^69 + 100*x^68 + 21*x^67 + 40*x^66 + 21*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 82*x^7 + 104*x^6 + 42*x^5 + 100*x^4 + 61*x^3 + 40*x^2 + 125*x + 102, x^75 + 41*x^73 + 18*x^72 + 98*x^71 + 120*x^70 + 90*x^69 + 76*x^68 + 69*x^67 + 120*x^66 + 37*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 34*x^7 + 120*x^6 + 26*x^5 + 76*x^4 + 109*x^3 + 120*x^2 + 13*x + 18, x^75 + 41*x^73 + 10*x^72 + 2*x^71 + 104*x^70 + 90*x^69 + 76*x^68 + 101*x^67 + 72*x^66 + 101*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 66*x^7 + 104*x^6 + 26*x^5 + 76*x^4 + 13*x^3 + 72*x^2 + 77*x + 90, x^75 + 41*x^73 + 58*x^72 + 50*x^71 + 120*x^70 + 74*x^69 + 60*x^68 + 117*x^67 + 120*x^66 + 53*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 114*x^7 + 120*x^6 + 10*x^5 + 60*x^4 + 29*x^3 + 120*x^2 + 29*x + 122, x^75 + 41*x^73 + 34*x^72 + 34*x^71 + 120*x^70 + 26*x^69 + 108*x^68 + 5*x^67 + 120*x^66 + 101*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 98*x^7 + 120*x^6 + 90*x^5 + 108*x^4 + 45*x^3 + 120*x^2 + 77*x + 98, x^75 + 41*x^73 + 70*x^72 + 50*x^71 + 72*x^70 + 10*x^69 + 68*x^68 + 117*x^67 + 72*x^66 + 117*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 114*x^7 + 72*x^6 + 74*x^5 + 68*x^4 + 29*x^3 + 72*x^2 + 93*x + 6, x^75 + 41*x^73 + 54*x^72 + 98*x^71 + 24*x^70 + 58*x^69 + 52*x^68 + 5*x^67 + 56*x^66 + 5*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 34*x^7 + 24*x^6 + 122*x^5 + 52*x^4 + 45*x^3 + 56*x^2 + 109*x + 102, x^75 + 41*x^73 + 74*x^72 + 50*x^71 + 56*x^70 + 10*x^69 + 92*x^68 + 117*x^67 + 56*x^66 + 117*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 114*x^7 + 56*x^6 + 74*x^5 + 92*x^4 + 29*x^3 + 56*x^2 + 93*x + 74, x^75 + 41*x^73 + 90*x^72 + 34*x^71 + 8*x^70 + 122*x^69 + 12*x^68 + 69*x^67 + 40*x^66 + 69*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 98*x^7 + 8*x^6 + 58*x^5 + 12*x^4 + 109*x^3 + 40*x^2 + 45*x + 74, x^75 + 41*x^73 + 66*x^72 + 34*x^71 + 120*x^70 + 90*x^69 + 108*x^68 + 5*x^67 + 120*x^66 + 37*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 98*x^7 + 120*x^6 + 26*x^5 + 108*x^4 + 45*x^3 + 120*x^2 + 13*x + 66, x^75 + 41*x^73 + 114*x^72 + 98*x^71 + 88*x^70 + 26*x^69 + 44*x^68 + 69*x^67 + 24*x^66 + 101*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 34*x^7 + 88*x^6 + 90*x^5 + 44*x^4 + 109*x^3 + 24*x^2 + 77*x + 82, x^75 + 41*x^73 + 50*x^72 + 82*x^71 + 8*x^70 + 74*x^69 + 92*x^68 + 21*x^67 + 40*x^66 + 117*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 18*x^7 + 8*x^6 + 10*x^5 + 92*x^4 + 61*x^3 + 40*x^2 + 93*x + 34, x^75 + 41*x^73 + 26*x^72 + 50*x^71 + 88*x^70 + 74*x^69 + 92*x^68 + 117*x^67 + 24*x^66 + 53*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 114*x^7 + 88*x^6 + 10*x^5 + 92*x^4 + 29*x^3 + 24*x^2 + 29*x + 122, x^75 + 41*x^73 + 62*x^72 + 34*x^71 + 72*x^70 + 26*x^69 + 20*x^68 + 5*x^67 + 72*x^66 + 101*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 98*x^7 + 72*x^6 + 90*x^5 + 20*x^4 + 45*x^3 + 72*x^2 + 77*x + 62, x^75 + 41*x^73 + 6*x^72 + 66*x^71 + 120*x^70 + 26*x^69 + 52*x^68 + 37*x^67 + 88*x^66 + 37*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 2*x^7 + 120*x^6 + 90*x^5 + 52*x^4 + 77*x^3 + 88*x^2 + 13*x + 22, x^75 + 41*x^73 + 34*x^72 + 114*x^71 + 40*x^70 + 42*x^69 + 28*x^68 + 117*x^67 + 8*x^66 + 21*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 50*x^7 + 40*x^6 + 106*x^5 + 28*x^4 + 29*x^3 + 8*x^2 + 125*x + 114, x^75 + 41*x^73 + 30*x^72 + 82*x^71 + 88*x^70 + 10*x^69 + 100*x^68 + 21*x^67 + 120*x^66 + 53*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 18*x^7 + 88*x^6 + 74*x^5 + 100*x^4 + 61*x^3 + 120*x^2 + 29*x + 78, x^75 + 41*x^73 + 26*x^72 + 50*x^71 + 120*x^70 + 10*x^69 + 60*x^68 + 117*x^67 + 120*x^66 + 117*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 114*x^7 + 120*x^6 + 74*x^5 + 60*x^4 + 29*x^3 + 120*x^2 + 93*x + 26, x^75 + 41*x^73 + 98*x^72 + 98*x^71 + 120*x^70 + 90*x^69 + 108*x^68 + 69*x^67 + 120*x^66 + 37*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 34*x^7 + 120*x^6 + 26*x^5 + 108*x^4 + 109*x^3 + 120*x^2 + 13*x + 34, x^75 + 41*x^73 + 86*x^72 + 34*x^71 + 56*x^70 + 58*x^69 + 84*x^68 + 69*x^67 + 24*x^66 + 5*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 98*x^7 + 56*x^6 + 122*x^5 + 84*x^4 + 109*x^3 + 24*x^2 + 109*x + 38, x^75 + 41*x^73 + 110*x^72 + 98*x^71 + 40*x^70 + 90*x^69 + 84*x^68 + 69*x^67 + 104*x^66 + 37*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 34*x^7 + 40*x^6 + 26*x^5 + 84*x^4 + 109*x^3 + 104*x^2 + 13*x + 78, x^75 + 41*x^73 + 114*x^72 + 114*x^71 + 72*x^70 + 42*x^69 + 92*x^68 + 117*x^67 + 104*x^66 + 21*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 50*x^7 + 72*x^6 + 106*x^5 + 92*x^4 + 29*x^3 + 104*x^2 + 125*x + 98, x^75 + 41*x^73 + 50*x^72 + 66*x^71 + 120*x^70 + 122*x^69 + 76*x^68 + 101*x^67 + 120*x^66 + 5*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 2*x^7 + 120*x^6 + 58*x^5 + 76*x^4 + 13*x^3 + 120*x^2 + 109*x + 114, x^75 + 41*x^73 + 126*x^72 + 98*x^71 + 104*x^70 + 90*x^69 + 52*x^68 + 69*x^67 + 40*x^66 + 37*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 34*x^7 + 104*x^6 + 26*x^5 + 52*x^4 + 109*x^3 + 40*x^2 + 13*x + 94, x^75 + 41*x^73 + 42*x^72 + 34*x^71 + 40*x^70 + 122*x^69 + 76*x^68 + 69*x^67 + 8*x^66 + 69*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 98*x^7 + 40*x^6 + 58*x^5 + 76*x^4 + 109*x^3 + 8*x^2 + 45*x + 58, x^75 + 41*x^73 + 42*x^72 + 18*x^71 + 120*x^70 + 106*x^69 + 92*x^68 + 21*x^67 + 120*x^66 + 21*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 82*x^7 + 120*x^6 + 42*x^5 + 92*x^4 + 61*x^3 + 120*x^2 + 125*x + 106, x^75 + 41*x^73 + 114*x^72 + 50*x^71 + 104*x^70 + 42*x^69 + 60*x^68 + 53*x^67 + 72*x^66 + 21*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 114*x^7 + 104*x^6 + 106*x^5 + 60*x^4 + 93*x^3 + 72*x^2 + 125*x + 2, x^75 + 41*x^73 + 78*x^72 + 82*x^71 + 56*x^70 + 10*x^69 + 36*x^68 + 21*x^67 + 24*x^66 + 53*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 18*x^7 + 56*x^6 + 74*x^5 + 36*x^4 + 61*x^3 + 24*x^2 + 29*x + 94, x^75 + 41*x^73 + 66*x^72 + 34*x^71 + 56*x^70 + 26*x^69 + 108*x^68 + 5*x^67 + 56*x^66 + 101*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 98*x^7 + 56*x^6 + 90*x^5 + 108*x^4 + 45*x^3 + 56*x^2 + 77*x + 66, x^75 + 41*x^73 + 70*x^72 + 82*x^71 + 40*x^70 + 42*x^69 + 36*x^68 + 85*x^67 + 104*x^66 + 85*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 18*x^7 + 40*x^6 + 106*x^5 + 36*x^4 + 125*x^3 + 104*x^2 + 61*x + 38, x^75 + 41*x^73 + 26*x^72 + 66*x^71 + 104*x^70 + 26*x^69 + 108*x^68 + 37*x^67 + 72*x^66 + 37*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 2*x^7 + 104*x^6 + 90*x^5 + 108*x^4 + 77*x^3 + 72*x^2 + 13*x + 42, x^75 + 41*x^73 + 90*x^72 + 50*x^71 + 88*x^70 + 10*x^69 + 28*x^68 + 117*x^67 + 24*x^66 + 117*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 114*x^7 + 88*x^6 + 74*x^5 + 28*x^4 + 29*x^3 + 24*x^2 + 93*x + 122, x^75 + 41*x^73 + 42*x^72 + 50*x^71 + 24*x^70 + 74*x^69 + 60*x^68 + 117*x^67 + 88*x^66 + 53*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 114*x^7 + 24*x^6 + 10*x^5 + 60*x^4 + 29*x^3 + 88*x^2 + 29*x + 10, x^75 + 41*x^73 + 78*x^72 + 66*x^71 + 72*x^70 + 122*x^69 + 116*x^68 + 101*x^67 + 72*x^66 + 5*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 2*x^7 + 72*x^6 + 58*x^5 + 116*x^4 + 13*x^3 + 72*x^2 + 109*x + 78, x^75 + 41*x^73 + 78*x^72 + 114*x^71 + 24*x^70 + 106*x^69 + 68*x^68 + 117*x^67 + 56*x^66 + 85*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 50*x^7 + 24*x^6 + 42*x^5 + 68*x^4 + 29*x^3 + 56*x^2 + 61*x + 62, x^75 + 41*x^73 + 58*x^72 + 82*x^71 + 56*x^70 + 106*x^69 + 124*x^68 + 85*x^67 + 56*x^66 + 21*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 18*x^7 + 56*x^6 + 42*x^5 + 124*x^4 + 125*x^3 + 56*x^2 + 125*x + 58, x^75 + 41*x^73 + 10*x^72 + 98*x^71 + 8*x^70 + 122*x^69 + 44*x^68 + 5*x^67 + 40*x^66 + 69*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 34*x^7 + 8*x^6 + 58*x^5 + 44*x^4 + 45*x^3 + 40*x^2 + 45*x + 122, x^75 + 41*x^73 + 74*x^72 + 114*x^71 + 24*x^70 + 10*x^69 + 124*x^68 + 53*x^67 + 88*x^66 + 117*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 50*x^7 + 24*x^6 + 74*x^5 + 124*x^4 + 93*x^3 + 88*x^2 + 93*x + 42, x^75 + 41*x^73 + 98*x^72 + 98*x^71 + 56*x^70 + 26*x^69 + 108*x^68 + 69*x^67 + 56*x^66 + 101*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 34*x^7 + 56*x^6 + 90*x^5 + 108*x^4 + 109*x^3 + 56*x^2 + 77*x + 34, x^75 + 41*x^73 + 102*x^72 + 50*x^71 + 40*x^70 + 10*x^69 + 100*x^68 + 117*x^67 + 104*x^66 + 117*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 114*x^7 + 40*x^6 + 74*x^5 + 100*x^4 + 29*x^3 + 104*x^2 + 93*x + 70, x^75 + 41*x^73 + 122*x^72 + 34*x^71 + 40*x^70 + 122*x^69 + 108*x^68 + 69*x^67 + 8*x^66 + 69*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 98*x^7 + 40*x^6 + 58*x^5 + 108*x^4 + 109*x^3 + 8*x^2 + 45*x + 74, x^75 + 41*x^73 + 6*x^72 + 82*x^71 + 104*x^70 + 106*x^69 + 36*x^68 + 85*x^67 + 40*x^66 + 21*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 18*x^7 + 104*x^6 + 42*x^5 + 36*x^4 + 125*x^3 + 40*x^2 + 125*x + 102, x^75 + 41*x^73 + 86*x^72 + 66*x^71 + 24*x^70 + 90*x^69 + 52*x^68 + 37*x^67 + 56*x^66 + 101*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 2*x^7 + 24*x^6 + 26*x^5 + 52*x^4 + 77*x^3 + 56*x^2 + 77*x + 70, x^75 + 41*x^73 + 62*x^72 + 50*x^71 + 120*x^70 + 42*x^69 + 4*x^68 + 53*x^67 + 88*x^66 + 21*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 114*x^7 + 120*x^6 + 106*x^5 + 4*x^4 + 93*x^3 + 88*x^2 + 125*x + 14, x^75 + 41*x^73 + 2*x^72 + 18*x^71 + 72*x^70 + 74*x^69 + 124*x^68 + 85*x^67 + 104*x^66 + 117*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 82*x^7 + 72*x^6 + 10*x^5 + 124*x^4 + 125*x^3 + 104*x^2 + 93*x + 50, x^75 + 41*x^73 + 126*x^72 + 82*x^71 + 120*x^70 + 74*x^69 + 4*x^68 + 21*x^67 + 88*x^66 + 117*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 18*x^7 + 120*x^6 + 10*x^5 + 4*x^4 + 61*x^3 + 88*x^2 + 93*x + 78, x^75 + 41*x^73 + 18*x^72 + 50*x^71 + 104*x^70 + 106*x^69 + 60*x^68 + 53*x^67 + 72*x^66 + 85*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 114*x^7 + 104*x^6 + 42*x^5 + 60*x^4 + 93*x^3 + 72*x^2 + 61*x + 98, x^75 + 41*x^73 + 58*x^72 + 34*x^71 + 104*x^70 + 122*x^69 + 44*x^68 + 69*x^67 + 72*x^66 + 69*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 98*x^7 + 104*x^6 + 58*x^5 + 44*x^4 + 109*x^3 + 72*x^2 + 45*x + 74, x^75 + 41*x^73 + 90*x^72 + 34*x^71 + 104*x^70 + 58*x^69 + 44*x^68 + 69*x^67 + 72*x^66 + 5*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 98*x^7 + 104*x^6 + 122*x^5 + 44*x^4 + 109*x^3 + 72*x^2 + 109*x + 42, x^75 + 41*x^73 + 90*x^72 + 50*x^71 + 56*x^70 + 74*x^69 + 60*x^68 + 117*x^67 + 56*x^66 + 53*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 114*x^7 + 56*x^6 + 10*x^5 + 60*x^4 + 29*x^3 + 56*x^2 + 29*x + 90, x^75 + 41*x^73 + 82*x^72 + 2*x^71 + 120*x^70 + 122*x^69 + 76*x^68 + 37*x^67 + 120*x^66 + 5*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 66*x^7 + 120*x^6 + 58*x^5 + 76*x^4 + 77*x^3 + 120*x^2 + 109*x + 82, x^75 + 41*x^73 + 38*x^72 + 66*x^71 + 120*x^70 + 26*x^69 + 116*x^68 + 37*x^67 + 88*x^66 + 37*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 2*x^7 + 120*x^6 + 90*x^5 + 116*x^4 + 77*x^3 + 88*x^2 + 13*x + 54, x^75 + 41*x^73 + 46*x^72 + 114*x^71 + 88*x^70 + 106*x^69 + 68*x^68 + 117*x^67 + 120*x^66 + 85*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 50*x^7 + 88*x^6 + 42*x^5 + 68*x^4 + 29*x^3 + 120*x^2 + 61*x + 94, x^75 + 41*x^73 + 118*x^72 + 114*x^71 + 40*x^70 + 10*x^69 + 68*x^68 + 53*x^67 + 104*x^66 + 117*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 50*x^7 + 40*x^6 + 74*x^5 + 68*x^4 + 93*x^3 + 104*x^2 + 93*x + 86, x^75 + 41*x^73 + 30*x^72 + 2*x^71 + 40*x^70 + 122*x^69 + 52*x^68 + 37*x^67 + 104*x^66 + 5*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 66*x^7 + 40*x^6 + 58*x^5 + 52*x^4 + 77*x^3 + 104*x^2 + 109*x + 62, x^75 + 41*x^73 + 102*x^72 + 18*x^71 + 72*x^70 + 106*x^69 + 4*x^68 + 21*x^67 + 72*x^66 + 21*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 82*x^7 + 72*x^6 + 42*x^5 + 4*x^4 + 61*x^3 + 72*x^2 + 125*x + 38, x^75 + 41*x^73 + 114*x^72 + 114*x^71 + 104*x^70 + 42*x^69 + 124*x^68 + 117*x^67 + 72*x^66 + 21*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 50*x^7 + 104*x^6 + 106*x^5 + 124*x^4 + 29*x^3 + 72*x^2 + 125*x + 66, x^75 + 41*x^73 + 42*x^72 + 114*x^71 + 56*x^70 + 74*x^69 + 28*x^68 + 53*x^67 + 56*x^66 + 53*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 50*x^7 + 56*x^6 + 10*x^5 + 28*x^4 + 93*x^3 + 56*x^2 + 29*x + 42, x^75 + 41*x^73 + 126*x^72 + 18*x^71 + 56*x^70 + 74*x^69 + 4*x^68 + 85*x^67 + 24*x^66 + 117*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 82*x^7 + 56*x^6 + 10*x^5 + 4*x^4 + 125*x^3 + 24*x^2 + 93*x + 78, x^75 + 41*x^73 + 102*x^72 + 114*x^71 + 40*x^70 + 74*x^69 + 100*x^68 + 53*x^67 + 104*x^66 + 53*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 50*x^7 + 40*x^6 + 10*x^5 + 100*x^4 + 93*x^3 + 104*x^2 + 29*x + 70, x^75 + 41*x^73 + 94*x^72 + 2*x^71 + 40*x^70 + 122*x^69 + 52*x^68 + 37*x^67 + 104*x^66 + 5*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 66*x^7 + 40*x^6 + 58*x^5 + 52*x^4 + 77*x^3 + 104*x^2 + 109*x + 126, x^75 + 41*x^73 + 82*x^72 + 98*x^71 + 88*x^70 + 90*x^69 + 44*x^68 + 69*x^67 + 24*x^66 + 37*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 34*x^7 + 88*x^6 + 26*x^5 + 44*x^4 + 109*x^3 + 24*x^2 + 13*x + 114, x^75 + 41*x^73 + 118*x^72 + 18*x^71 + 72*x^70 + 42*x^69 + 100*x^68 + 21*x^67 + 72*x^66 + 85*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 82*x^7 + 72*x^6 + 106*x^5 + 100*x^4 + 61*x^3 + 72*x^2 + 61*x + 54, x^75 + 41*x^73 + 42*x^72 + 114*x^71 + 56*x^70 + 10*x^69 + 92*x^68 + 53*x^67 + 56*x^66 + 117*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 50*x^7 + 56*x^6 + 74*x^5 + 92*x^4 + 93*x^3 + 56*x^2 + 93*x + 106, x^75 + 41*x^73 + 18*x^72 + 66*x^71 + 88*x^70 + 122*x^69 + 108*x^68 + 101*x^67 + 24*x^66 + 5*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 2*x^7 + 88*x^6 + 58*x^5 + 108*x^4 + 13*x^3 + 24*x^2 + 109*x + 114, x^75 + 41*x^73 + 74*x^72 + 98*x^71 + 104*x^70 + 122*x^69 + 12*x^68 + 5*x^67 + 72*x^66 + 69*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 34*x^7 + 104*x^6 + 58*x^5 + 12*x^4 + 45*x^3 + 72*x^2 + 45*x + 90, x^75 + 41*x^73 + 50*x^72 + 18*x^71 + 104*x^70 + 74*x^69 + 124*x^68 + 85*x^67 + 72*x^66 + 117*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 82*x^7 + 104*x^6 + 10*x^5 + 124*x^4 + 125*x^3 + 72*x^2 + 93*x + 2, x^75 + 41*x^73 + 82*x^72 + 2*x^71 + 56*x^70 + 122*x^69 + 12*x^68 + 37*x^67 + 56*x^66 + 5*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 66*x^7 + 56*x^6 + 58*x^5 + 12*x^4 + 77*x^3 + 56*x^2 + 109*x + 18, x^75 + 41*x^73 + 78*x^72 + 82*x^71 + 24*x^70 + 74*x^69 + 68*x^68 + 21*x^67 + 56*x^66 + 117*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 18*x^7 + 24*x^6 + 10*x^5 + 68*x^4 + 61*x^3 + 56*x^2 + 93*x + 62, x^75 + 41*x^73 + 34*x^72 + 34*x^71 + 24*x^70 + 90*x^69 + 76*x^68 + 5*x^67 + 88*x^66 + 37*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 98*x^7 + 24*x^6 + 26*x^5 + 76*x^4 + 45*x^3 + 88*x^2 + 13*x + 2, x^75 + 41*x^73 + 62*x^72 + 66*x^71 + 40*x^70 + 58*x^69 + 116*x^68 + 101*x^67 + 104*x^66 + 69*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 2*x^7 + 40*x^6 + 122*x^5 + 116*x^4 + 13*x^3 + 104*x^2 + 45*x + 94, x^75 + 41*x^73 + 86*x^72 + 50*x^71 + 8*x^70 + 74*x^69 + 100*x^68 + 117*x^67 + 8*x^66 + 53*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 114*x^7 + 8*x^6 + 10*x^5 + 100*x^4 + 29*x^3 + 8*x^2 + 29*x + 86, x^75 + 41*x^73 + 50*x^72 + 18*x^71 + 104*x^70 + 10*x^69 + 60*x^68 + 85*x^67 + 72*x^66 + 53*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 82*x^7 + 104*x^6 + 74*x^5 + 60*x^4 + 125*x^3 + 72*x^2 + 29*x + 66, x^75 + 41*x^73 + 42*x^72 + 98*x^71 + 104*x^70 + 58*x^69 + 12*x^68 + 5*x^67 + 72*x^66 + 5*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 34*x^7 + 104*x^6 + 122*x^5 + 12*x^4 + 45*x^3 + 72*x^2 + 109*x + 122, x^75 + 41*x^73 + 58*x^72 + 34*x^71 + 104*x^70 + 58*x^69 + 108*x^68 + 69*x^67 + 72*x^66 + 5*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 98*x^7 + 104*x^6 + 122*x^5 + 108*x^4 + 109*x^3 + 72*x^2 + 109*x + 10, x^75 + 41*x^73 + 6*x^72 + 34*x^71 + 24*x^70 + 58*x^69 + 20*x^68 + 69*x^67 + 56*x^66 + 5*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 98*x^7 + 24*x^6 + 122*x^5 + 20*x^4 + 109*x^3 + 56*x^2 + 109*x + 54, x^75 + 41*x^73 + 46*x^72 + 18*x^71 + 88*x^70 + 74*x^69 + 4*x^68 + 85*x^67 + 120*x^66 + 117*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 82*x^7 + 88*x^6 + 10*x^5 + 4*x^4 + 125*x^3 + 120*x^2 + 93*x + 30, x^75 + 41*x^73 + 62*x^72 + 98*x^71 + 72*x^70 + 90*x^69 + 20*x^68 + 69*x^67 + 72*x^66 + 37*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 34*x^7 + 72*x^6 + 26*x^5 + 20*x^4 + 109*x^3 + 72*x^2 + 13*x + 62, x^75 + 41*x^73 + 82*x^72 + 2*x^71 + 56*x^70 + 58*x^69 + 76*x^68 + 37*x^67 + 56*x^66 + 69*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 66*x^7 + 56*x^6 + 122*x^5 + 76*x^4 + 77*x^3 + 56*x^2 + 45*x + 82, x^75 + 41*x^73 + 22*x^72 + 98*x^71 + 120*x^70 + 122*x^69 + 20*x^68 + 5*x^67 + 88*x^66 + 69*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 34*x^7 + 120*x^6 + 58*x^5 + 20*x^4 + 45*x^3 + 88*x^2 + 45*x + 38, x^75 + 41*x^73 + 10*x^72 + 34*x^71 + 104*x^70 + 58*x^69 + 12*x^68 + 69*x^67 + 72*x^66 + 5*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 98*x^7 + 104*x^6 + 122*x^5 + 12*x^4 + 109*x^3 + 72*x^2 + 109*x + 26, x^75 + 41*x^73 + 50*x^72 + 18*x^71 + 40*x^70 + 74*x^69 + 60*x^68 + 85*x^67 + 8*x^66 + 117*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 82*x^7 + 40*x^6 + 10*x^5 + 60*x^4 + 125*x^3 + 8*x^2 + 93*x + 66, x^75 + 41*x^73 + 22*x^72 + 2*x^71 + 56*x^70 + 90*x^69 + 20*x^68 + 101*x^67 + 24*x^66 + 101*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 66*x^7 + 56*x^6 + 26*x^5 + 20*x^4 + 13*x^3 + 24*x^2 + 77*x + 38, x^75 + 41*x^73 + 42*x^72 + 82*x^71 + 88*x^70 + 42*x^69 + 60*x^68 + 85*x^67 + 24*x^66 + 85*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 18*x^7 + 88*x^6 + 106*x^5 + 60*x^4 + 125*x^3 + 24*x^2 + 61*x + 10, x^75 + 41*x^73 + 50*x^72 + 98*x^71 + 56*x^70 + 90*x^69 + 76*x^68 + 69*x^67 + 56*x^66 + 37*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 34*x^7 + 56*x^6 + 26*x^5 + 76*x^4 + 109*x^3 + 56*x^2 + 13*x + 114, x^75 + 41*x^73 + 78*x^72 + 114*x^71 + 88*x^70 + 42*x^69 + 68*x^68 + 117*x^67 + 120*x^66 + 21*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 50*x^7 + 88*x^6 + 106*x^5 + 68*x^4 + 29*x^3 + 120*x^2 + 125*x + 62, x^75 + 41*x^73 + 30*x^72 + 98*x^71 + 40*x^70 + 26*x^69 + 116*x^68 + 69*x^67 + 104*x^66 + 101*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 34*x^7 + 40*x^6 + 90*x^5 + 116*x^4 + 109*x^3 + 104*x^2 + 77*x + 126, x^75 + 41*x^73 + 18*x^72 + 114*x^71 + 72*x^70 + 42*x^69 + 28*x^68 + 117*x^67 + 104*x^66 + 21*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 50*x^7 + 72*x^6 + 106*x^5 + 28*x^4 + 29*x^3 + 104*x^2 + 125*x + 2, x^75 + 41*x^73 + 102*x^72 + 2*x^71 + 24*x^70 + 26*x^69 + 84*x^68 + 101*x^67 + 56*x^66 + 37*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 66*x^7 + 24*x^6 + 90*x^5 + 84*x^4 + 13*x^3 + 56*x^2 + 13*x + 22, x^75 + 41*x^73 + 34*x^72 + 18*x^71 + 104*x^70 + 74*x^69 + 92*x^68 + 85*x^67 + 72*x^66 + 117*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 82*x^7 + 104*x^6 + 10*x^5 + 92*x^4 + 125*x^3 + 72*x^2 + 93*x + 50, x^75 + 41*x^73 + 10*x^72 + 98*x^71 + 104*x^70 + 122*x^69 + 12*x^68 + 5*x^67 + 72*x^66 + 69*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 34*x^7 + 104*x^6 + 58*x^5 + 12*x^4 + 45*x^3 + 72*x^2 + 45*x + 26, x^75 + 41*x^73 + 26*x^72 + 98*x^71 + 8*x^70 + 58*x^69 + 12*x^68 + 5*x^67 + 40*x^66 + 5*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 34*x^7 + 8*x^6 + 122*x^5 + 12*x^4 + 45*x^3 + 40*x^2 + 109*x + 10, x^75 + 41*x^73 + 14*x^72 + 82*x^71 + 24*x^70 + 74*x^69 + 68*x^68 + 21*x^67 + 56*x^66 + 117*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 18*x^7 + 24*x^6 + 10*x^5 + 68*x^4 + 61*x^3 + 56*x^2 + 93*x + 126, x^75 + 41*x^73 + 98*x^72 + 82*x^71 + 8*x^70 + 74*x^69 + 60*x^68 + 21*x^67 + 40*x^66 + 117*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 18*x^7 + 8*x^6 + 10*x^5 + 60*x^4 + 61*x^3 + 40*x^2 + 93*x + 18, x^75 + 41*x^73 + 86*x^72 + 18*x^71 + 72*x^70 + 42*x^69 + 36*x^68 + 21*x^67 + 72*x^66 + 85*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 82*x^7 + 72*x^6 + 106*x^5 + 36*x^4 + 61*x^3 + 72*x^2 + 61*x + 22, x^75 + 41*x^73 + 70*x^72 + 34*x^71 + 120*x^70 + 122*x^69 + 52*x^68 + 69*x^67 + 88*x^66 + 69*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 98*x^7 + 120*x^6 + 58*x^5 + 52*x^4 + 109*x^3 + 88*x^2 + 45*x + 86, x^75 + 41*x^73 + 102*x^72 + 82*x^71 + 104*x^70 + 106*x^69 + 100*x^68 + 85*x^67 + 40*x^66 + 21*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 18*x^7 + 104*x^6 + 42*x^5 + 100*x^4 + 125*x^3 + 40*x^2 + 125*x + 70, x^75 + 41*x^73 + 110*x^72 + 2*x^71 + 8*x^70 + 122*x^69 + 52*x^68 + 37*x^67 + 8*x^66 + 5*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 66*x^7 + 8*x^6 + 58*x^5 + 52*x^4 + 77*x^3 + 8*x^2 + 109*x + 110, x^75 + 41*x^73 + 82*x^72 + 66*x^71 + 88*x^70 + 58*x^69 + 44*x^68 + 101*x^67 + 24*x^66 + 69*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 2*x^7 + 88*x^6 + 122*x^5 + 44*x^4 + 13*x^3 + 24*x^2 + 45*x + 114, x^75 + 41*x^73 + 42*x^72 + 66*x^71 + 72*x^70 + 26*x^69 + 108*x^68 + 37*x^67 + 104*x^66 + 37*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 2*x^7 + 72*x^6 + 90*x^5 + 108*x^4 + 77*x^3 + 104*x^2 + 13*x + 26, x^75 + 41*x^73 + 2*x^72 + 98*x^71 + 24*x^70 + 90*x^69 + 76*x^68 + 69*x^67 + 88*x^66 + 37*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 34*x^7 + 24*x^6 + 26*x^5 + 76*x^4 + 109*x^3 + 88*x^2 + 13*x + 34, x^75 + 41*x^73 + 98*x^72 + 34*x^71 + 88*x^70 + 90*x^69 + 12*x^68 + 5*x^67 + 24*x^66 + 37*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 98*x^7 + 88*x^6 + 26*x^5 + 12*x^4 + 45*x^3 + 24*x^2 + 13*x + 2, x^75 + 41*x^73 + 50*x^72 + 34*x^71 + 88*x^70 + 90*x^69 + 44*x^68 + 5*x^67 + 24*x^66 + 37*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 98*x^7 + 88*x^6 + 26*x^5 + 44*x^4 + 45*x^3 + 24*x^2 + 13*x + 18, x^75 + 41*x^73 + 118*x^72 + 98*x^71 + 56*x^70 + 122*x^69 + 20*x^68 + 5*x^67 + 24*x^66 + 69*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 34*x^7 + 56*x^6 + 58*x^5 + 20*x^4 + 45*x^3 + 24*x^2 + 45*x + 70, x^75 + 41*x^73 + 118*x^72 + 34*x^71 + 24*x^70 + 122*x^69 + 52*x^68 + 69*x^67 + 56*x^66 + 69*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 98*x^7 + 24*x^6 + 58*x^5 + 52*x^4 + 109*x^3 + 56*x^2 + 45*x + 38, x^75 + 41*x^73 + 62*x^72 + 34*x^71 + 104*x^70 + 26*x^69 + 52*x^68 + 5*x^67 + 40*x^66 + 101*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 98*x^7 + 104*x^6 + 90*x^5 + 52*x^4 + 45*x^3 + 40*x^2 + 77*x + 30, x^75 + 41*x^73 + 34*x^72 + 82*x^71 + 104*x^70 + 10*x^69 + 92*x^68 + 21*x^67 + 72*x^66 + 53*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 18*x^7 + 104*x^6 + 74*x^5 + 92*x^4 + 61*x^3 + 72*x^2 + 29*x + 50, x^75 + 41*x^73 + 38*x^72 + 82*x^71 + 8*x^70 + 106*x^69 + 4*x^68 + 85*x^67 + 8*x^66 + 21*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 18*x^7 + 8*x^6 + 42*x^5 + 4*x^4 + 125*x^3 + 8*x^2 + 125*x + 102, x^75 + 41*x^73 + 6*x^72 + 98*x^71 + 120*x^70 + 58*x^69 + 52*x^68 + 5*x^67 + 88*x^66 + 5*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 34*x^7 + 120*x^6 + 122*x^5 + 52*x^4 + 45*x^3 + 88*x^2 + 109*x + 22, x^75 + 41*x^73 + 66*x^72 + 114*x^71 + 8*x^70 + 42*x^69 + 60*x^68 + 117*x^67 + 40*x^66 + 21*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 50*x^7 + 8*x^6 + 106*x^5 + 60*x^4 + 29*x^3 + 40*x^2 + 125*x + 50, x^75 + 41*x^73 + 50*x^72 + 50*x^71 + 104*x^70 + 42*x^69 + 60*x^68 + 53*x^67 + 72*x^66 + 21*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 114*x^7 + 104*x^6 + 106*x^5 + 60*x^4 + 93*x^3 + 72*x^2 + 125*x + 66, x^75 + 41*x^73 + 30*x^72 + 82*x^71 + 56*x^70 + 10*x^69 + 68*x^68 + 21*x^67 + 24*x^66 + 53*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 18*x^7 + 56*x^6 + 74*x^5 + 68*x^4 + 61*x^3 + 24*x^2 + 29*x + 110, x^75 + 41*x^73 + 14*x^72 + 114*x^71 + 88*x^70 + 42*x^69 + 68*x^68 + 117*x^67 + 120*x^66 + 21*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 50*x^7 + 88*x^6 + 106*x^5 + 68*x^4 + 29*x^3 + 120*x^2 + 125*x + 126, x^75 + 41*x^73 + 50*x^72 + 66*x^71 + 24*x^70 + 58*x^69 + 44*x^68 + 101*x^67 + 88*x^66 + 69*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 2*x^7 + 24*x^6 + 122*x^5 + 44*x^4 + 13*x^3 + 88*x^2 + 45*x + 18, x^75 + 41*x^73 + 46*x^72 + 18*x^71 + 56*x^70 + 74*x^69 + 100*x^68 + 85*x^67 + 24*x^66 + 117*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 82*x^7 + 56*x^6 + 10*x^5 + 100*x^4 + 125*x^3 + 24*x^2 + 93*x + 62, x^75 + 41*x^73 + 110*x^72 + 50*x^71 + 24*x^70 + 106*x^69 + 68*x^68 + 53*x^67 + 56*x^66 + 85*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 114*x^7 + 24*x^6 + 42*x^5 + 68*x^4 + 93*x^3 + 56*x^2 + 61*x + 30, x^75 + 41*x^73 + 22*x^72 + 114*x^71 + 72*x^70 + 10*x^69 + 36*x^68 + 53*x^67 + 72*x^66 + 117*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 50*x^7 + 72*x^6 + 74*x^5 + 36*x^4 + 93*x^3 + 72*x^2 + 93*x + 86, x^75 + 41*x^73 + 90*x^72 + 66*x^71 + 40*x^70 + 26*x^69 + 44*x^68 + 37*x^67 + 8*x^66 + 37*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 2*x^7 + 40*x^6 + 90*x^5 + 44*x^4 + 77*x^3 + 8*x^2 + 13*x + 42, x^75 + 41*x^73 + 22*x^72 + 34*x^71 + 56*x^70 + 58*x^69 + 84*x^68 + 69*x^67 + 24*x^66 + 5*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 98*x^7 + 56*x^6 + 122*x^5 + 84*x^4 + 109*x^3 + 24*x^2 + 109*x + 102, x^75 + 41*x^73 + 74*x^72 + 114*x^71 + 120*x^70 + 74*x^69 + 28*x^68 + 53*x^67 + 120*x^66 + 53*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 50*x^7 + 120*x^6 + 10*x^5 + 28*x^4 + 93*x^3 + 120*x^2 + 29*x + 10, x^75 + 41*x^73 + 122*x^72 + 50*x^71 + 88*x^70 + 10*x^69 + 92*x^68 + 117*x^67 + 24*x^66 + 117*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 114*x^7 + 88*x^6 + 74*x^5 + 92*x^4 + 29*x^3 + 24*x^2 + 93*x + 26, x^75 + 41*x^73 + 22*x^72 + 18*x^71 + 72*x^70 + 106*x^69 + 100*x^68 + 21*x^67 + 72*x^66 + 21*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 82*x^7 + 72*x^6 + 42*x^5 + 100*x^4 + 61*x^3 + 72*x^2 + 125*x + 22, x^75 + 41*x^73 + 122*x^72 + 82*x^71 + 24*x^70 + 42*x^69 + 28*x^68 + 85*x^67 + 88*x^66 + 85*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 18*x^7 + 24*x^6 + 106*x^5 + 28*x^4 + 125*x^3 + 88*x^2 + 61*x + 90, x^75 + 41*x^73 + 114*x^72 + 82*x^71 + 72*x^70 + 74*x^69 + 28*x^68 + 21*x^67 + 104*x^66 + 117*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 18*x^7 + 72*x^6 + 10*x^5 + 28*x^4 + 61*x^3 + 104*x^2 + 93*x + 34, x^75 + 41*x^73 + 114*x^72 + 98*x^71 + 24*x^70 + 26*x^69 + 108*x^68 + 69*x^67 + 88*x^66 + 101*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 34*x^7 + 24*x^6 + 90*x^5 + 108*x^4 + 109*x^3 + 88*x^2 + 77*x + 18, x^75 + 41*x^73 + 94*x^72 + 66*x^71 + 104*x^70 + 122*x^69 + 52*x^68 + 101*x^67 + 40*x^66 + 5*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 2*x^7 + 104*x^6 + 58*x^5 + 52*x^4 + 13*x^3 + 40*x^2 + 109*x + 126, x^75 + 41*x^73 + 102*x^72 + 50*x^71 + 8*x^70 + 74*x^69 + 4*x^68 + 117*x^67 + 8*x^66 + 53*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 114*x^7 + 8*x^6 + 10*x^5 + 4*x^4 + 29*x^3 + 8*x^2 + 29*x + 38, x^75 + 41*x^73 + 30*x^72 + 82*x^71 + 120*x^70 + 74*x^69 + 68*x^68 + 21*x^67 + 88*x^66 + 117*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 18*x^7 + 120*x^6 + 10*x^5 + 68*x^4 + 61*x^3 + 88*x^2 + 93*x + 110, x^75 + 41*x^73 + 126*x^72 + 66*x^71 + 40*x^70 + 58*x^69 + 116*x^68 + 101*x^67 + 104*x^66 + 69*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 2*x^7 + 40*x^6 + 122*x^5 + 116*x^4 + 13*x^3 + 104*x^2 + 45*x + 30, x^75 + 41*x^73 + 126*x^72 + 50*x^71 + 88*x^70 + 42*x^69 + 100*x^68 + 53*x^67 + 120*x^66 + 21*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 114*x^7 + 88*x^6 + 106*x^5 + 100*x^4 + 93*x^3 + 120*x^2 + 125*x + 110, x^75 + 41*x^73 + 26*x^72 + 50*x^71 + 56*x^70 + 74*x^69 + 60*x^68 + 117*x^67 + 56*x^66 + 53*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 114*x^7 + 56*x^6 + 10*x^5 + 60*x^4 + 29*x^3 + 56*x^2 + 29*x + 26, x^75 + 41*x^73 + 86*x^72 + 114*x^71 + 104*x^70 + 74*x^69 + 4*x^68 + 53*x^67 + 40*x^66 + 53*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 50*x^7 + 104*x^6 + 10*x^5 + 4*x^4 + 93*x^3 + 40*x^2 + 29*x + 54, x^75 + 41*x^73 + 50*x^72 + 66*x^71 + 88*x^70 + 58*x^69 + 108*x^68 + 101*x^67 + 24*x^66 + 69*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 2*x^7 + 88*x^6 + 122*x^5 + 108*x^4 + 13*x^3 + 24*x^2 + 45*x + 82, x^75 + 41*x^73 + 22*x^72 + 98*x^71 + 88*x^70 + 122*x^69 + 116*x^68 + 5*x^67 + 120*x^66 + 69*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 34*x^7 + 88*x^6 + 58*x^5 + 116*x^4 + 45*x^3 + 120*x^2 + 45*x + 70, x^75 + 41*x^73 + 42*x^72 + 2*x^71 + 8*x^70 + 26*x^69 + 108*x^68 + 101*x^67 + 40*x^66 + 37*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 66*x^7 + 8*x^6 + 90*x^5 + 108*x^4 + 13*x^3 + 40*x^2 + 13*x + 26, x^75 + 41*x^73 + 58*x^72 + 2*x^71 + 72*x^70 + 90*x^69 + 12*x^68 + 101*x^67 + 104*x^66 + 101*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 66*x^7 + 72*x^6 + 26*x^5 + 12*x^4 + 13*x^3 + 104*x^2 + 77*x + 106, x^75 + 41*x^73 + 34*x^72 + 114*x^71 + 72*x^70 + 106*x^69 + 124*x^68 + 117*x^67 + 104*x^66 + 85*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 50*x^7 + 72*x^6 + 42*x^5 + 124*x^4 + 29*x^3 + 104*x^2 + 61*x + 18, x^75 + 41*x^73 + 46*x^72 + 114*x^71 + 56*x^70 + 106*x^69 + 36*x^68 + 117*x^67 + 24*x^66 + 85*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 50*x^7 + 56*x^6 + 42*x^5 + 36*x^4 + 29*x^3 + 24*x^2 + 61*x + 126, x^75 + 41*x^73 + 78*x^72 + 2*x^71 + 8*x^70 + 58*x^69 + 52*x^68 + 37*x^67 + 8*x^66 + 69*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 66*x^7 + 8*x^6 + 122*x^5 + 52*x^4 + 77*x^3 + 8*x^2 + 45*x + 14, x^75 + 41*x^73 + 14*x^72 + 66*x^71 + 104*x^70 + 122*x^69 + 20*x^68 + 101*x^67 + 40*x^66 + 5*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 2*x^7 + 104*x^6 + 58*x^5 + 20*x^4 + 13*x^3 + 40*x^2 + 109*x + 110, x^75 + 41*x^73 + 98*x^72 + 34*x^71 + 24*x^70 + 26*x^69 + 12*x^68 + 5*x^67 + 88*x^66 + 101*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 98*x^7 + 24*x^6 + 90*x^5 + 12*x^4 + 45*x^3 + 88*x^2 + 77*x + 2, x^75 + 41*x^73 + 58*x^72 + 50*x^71 + 88*x^70 + 74*x^69 + 28*x^68 + 117*x^67 + 24*x^66 + 53*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 114*x^7 + 88*x^6 + 10*x^5 + 28*x^4 + 29*x^3 + 24*x^2 + 29*x + 26, x^75 + 41*x^73 + 86*x^72 + 82*x^71 + 104*x^70 + 42*x^69 + 4*x^68 + 85*x^67 + 40*x^66 + 85*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 18*x^7 + 104*x^6 + 106*x^5 + 4*x^4 + 125*x^3 + 40*x^2 + 61*x + 54, x^75 + 41*x^73 + 70*x^72 + 98*x^71 + 24*x^70 + 58*x^69 + 84*x^68 + 5*x^67 + 56*x^66 + 5*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 34*x^7 + 24*x^6 + 122*x^5 + 84*x^4 + 45*x^3 + 56*x^2 + 109*x + 54, x^75 + 41*x^73 + 26*x^72 + 98*x^71 + 104*x^70 + 58*x^69 + 108*x^68 + 5*x^67 + 72*x^66 + 5*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 34*x^7 + 104*x^6 + 122*x^5 + 108*x^4 + 45*x^3 + 72*x^2 + 109*x + 42, x^75 + 41*x^73 + 58*x^72 + 98*x^71 + 40*x^70 + 122*x^69 + 44*x^68 + 5*x^67 + 8*x^66 + 69*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 34*x^7 + 40*x^6 + 58*x^5 + 44*x^4 + 45*x^3 + 8*x^2 + 45*x + 74, x^75 + 41*x^73 + 46*x^72 + 98*x^71 + 72*x^70 + 26*x^69 + 52*x^68 + 69*x^67 + 72*x^66 + 101*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 34*x^7 + 72*x^6 + 90*x^5 + 52*x^4 + 109*x^3 + 72*x^2 + 77*x + 46, x^75 + 41*x^73 + 90*x^72 + 98*x^71 + 40*x^70 + 58*x^69 + 44*x^68 + 5*x^67 + 8*x^66 + 5*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 34*x^7 + 40*x^6 + 122*x^5 + 44*x^4 + 45*x^3 + 8*x^2 + 109*x + 42, x^75 + 41*x^73 + 14*x^72 + 18*x^71 + 120*x^70 + 74*x^69 + 100*x^68 + 85*x^67 + 88*x^66 + 117*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 82*x^7 + 120*x^6 + 10*x^5 + 100*x^4 + 125*x^3 + 88*x^2 + 93*x + 94, x^75 + 41*x^73 + 98*x^72 + 2*x^71 + 120*x^70 + 58*x^69 + 44*x^68 + 37*x^67 + 120*x^66 + 69*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 66*x^7 + 120*x^6 + 122*x^5 + 44*x^4 + 77*x^3 + 120*x^2 + 45*x + 98, x^75 + 41*x^73 + 38*x^72 + 98*x^71 + 56*x^70 + 122*x^69 + 116*x^68 + 5*x^67 + 24*x^66 + 69*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 34*x^7 + 56*x^6 + 58*x^5 + 116*x^4 + 45*x^3 + 24*x^2 + 45*x + 54, x^75 + 41*x^73 + 30*x^72 + 2*x^71 + 8*x^70 + 122*x^69 + 20*x^68 + 37*x^67 + 8*x^66 + 5*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 66*x^7 + 8*x^6 + 58*x^5 + 20*x^4 + 77*x^3 + 8*x^2 + 109*x + 94, x^75 + 41*x^73 + 34*x^72 + 66*x^71 + 88*x^70 + 122*x^69 + 12*x^68 + 101*x^67 + 24*x^66 + 5*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 2*x^7 + 88*x^6 + 58*x^5 + 12*x^4 + 13*x^3 + 24*x^2 + 109*x + 66, x^75 + 41*x^73 + 30*x^72 + 2*x^71 + 104*x^70 + 58*x^69 + 52*x^68 + 37*x^67 + 40*x^66 + 69*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 66*x^7 + 104*x^6 + 122*x^5 + 52*x^4 + 77*x^3 + 40*x^2 + 45*x + 62, x^75 + 41*x^73 + 18*x^72 + 114*x^71 + 8*x^70 + 106*x^69 + 28*x^68 + 117*x^67 + 40*x^66 + 85*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 50*x^7 + 8*x^6 + 42*x^5 + 28*x^4 + 29*x^3 + 40*x^2 + 61*x + 2, x^75 + 41*x^73 + 74*x^72 + 66*x^71 + 72*x^70 + 90*x^69 + 108*x^68 + 37*x^67 + 104*x^66 + 101*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 2*x^7 + 72*x^6 + 26*x^5 + 108*x^4 + 77*x^3 + 104*x^2 + 77*x + 122, x^75 + 41*x^73 + 6*x^72 + 82*x^71 + 8*x^70 + 106*x^69 + 68*x^68 + 85*x^67 + 8*x^66 + 21*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 18*x^7 + 8*x^6 + 42*x^5 + 68*x^4 + 125*x^3 + 8*x^2 + 125*x + 70, x^75 + 41*x^73 + 62*x^72 + 114*x^71 + 24*x^70 + 42*x^69 + 100*x^68 + 117*x^67 + 56*x^66 + 21*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 50*x^7 + 24*x^6 + 106*x^5 + 100*x^4 + 29*x^3 + 56*x^2 + 125*x + 46, x^75 + 41*x^73 + 62*x^72 + 114*x^71 + 88*x^70 + 106*x^69 + 100*x^68 + 117*x^67 + 120*x^66 + 85*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 50*x^7 + 88*x^6 + 42*x^5 + 100*x^4 + 29*x^3 + 120*x^2 + 61*x + 46, x^75 + 41*x^73 + 46*x^72 + 98*x^71 + 40*x^70 + 90*x^69 + 84*x^68 + 69*x^67 + 104*x^66 + 37*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 34*x^7 + 40*x^6 + 26*x^5 + 84*x^4 + 109*x^3 + 104*x^2 + 13*x + 14, x^75 + 41*x^73 + 2*x^72 + 18*x^71 + 104*x^70 + 74*x^69 + 28*x^68 + 85*x^67 + 72*x^66 + 117*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 82*x^7 + 104*x^6 + 10*x^5 + 28*x^4 + 125*x^3 + 72*x^2 + 93*x + 18, x^75 + 41*x^73 + 2*x^72 + 18*x^71 + 104*x^70 + 10*x^69 + 92*x^68 + 85*x^67 + 72*x^66 + 53*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 82*x^7 + 104*x^6 + 74*x^5 + 92*x^4 + 125*x^3 + 72*x^2 + 29*x + 82, x^75 + 41*x^73 + 26*x^72 + 98*x^71 + 72*x^70 + 58*x^69 + 76*x^68 + 5*x^67 + 104*x^66 + 5*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 34*x^7 + 72*x^6 + 122*x^5 + 76*x^4 + 45*x^3 + 104*x^2 + 109*x + 74, x^75 + 41*x^73 + 70*x^72 + 2*x^71 + 24*x^70 + 90*x^69 + 84*x^68 + 101*x^67 + 56*x^66 + 101*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 66*x^7 + 24*x^6 + 26*x^5 + 84*x^4 + 13*x^3 + 56*x^2 + 77*x + 54, x^75 + 41*x^73 + 6*x^72 + 114*x^71 + 104*x^70 + 74*x^69 + 100*x^68 + 53*x^67 + 40*x^66 + 53*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 50*x^7 + 104*x^6 + 10*x^5 + 100*x^4 + 93*x^3 + 40*x^2 + 29*x + 38, x^75 + 41*x^73 + 86*x^72 + 2*x^71 + 88*x^70 + 90*x^69 + 52*x^68 + 101*x^67 + 120*x^66 + 101*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 66*x^7 + 88*x^6 + 26*x^5 + 52*x^4 + 13*x^3 + 120*x^2 + 77*x + 70, x^75 + 41*x^73 + 42*x^72 + 114*x^71 + 24*x^70 + 74*x^69 + 124*x^68 + 53*x^67 + 88*x^66 + 53*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 50*x^7 + 24*x^6 + 10*x^5 + 124*x^4 + 93*x^3 + 88*x^2 + 29*x + 74, x^75 + 41*x^73 + 18*x^72 + 66*x^71 + 24*x^70 + 58*x^69 + 108*x^68 + 101*x^67 + 88*x^66 + 69*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 2*x^7 + 24*x^6 + 122*x^5 + 108*x^4 + 13*x^3 + 88*x^2 + 45*x + 114, x^75 + 41*x^73 + 30*x^72 + 114*x^71 + 56*x^70 + 106*x^69 + 4*x^68 + 117*x^67 + 24*x^66 + 85*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 50*x^7 + 56*x^6 + 42*x^5 + 4*x^4 + 29*x^3 + 24*x^2 + 61*x + 46, x^75 + 41*x^73 + 86*x^72 + 34*x^71 + 120*x^70 + 58*x^69 + 20*x^68 + 69*x^67 + 88*x^66 + 5*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 98*x^7 + 120*x^6 + 122*x^5 + 20*x^4 + 109*x^3 + 88*x^2 + 109*x + 102, x^75 + 41*x^73 + 74*x^72 + 82*x^71 + 120*x^70 + 42*x^69 + 28*x^68 + 85*x^67 + 120*x^66 + 85*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 18*x^7 + 120*x^6 + 106*x^5 + 28*x^4 + 125*x^3 + 120*x^2 + 61*x + 10, x^75 + 41*x^73 + 122*x^72 + 34*x^71 + 104*x^70 + 58*x^69 + 108*x^68 + 69*x^67 + 72*x^66 + 5*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 98*x^7 + 104*x^6 + 122*x^5 + 108*x^4 + 109*x^3 + 72*x^2 + 109*x + 74, x^75 + 41*x^73 + 74*x^72 + 50*x^71 + 56*x^70 + 74*x^69 + 28*x^68 + 117*x^67 + 56*x^66 + 53*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 114*x^7 + 56*x^6 + 10*x^5 + 28*x^4 + 29*x^3 + 56*x^2 + 29*x + 10, x^75 + 41*x^73 + 126*x^72 + 18*x^71 + 56*x^70 + 10*x^69 + 68*x^68 + 85*x^67 + 24*x^66 + 53*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 82*x^7 + 56*x^6 + 74*x^5 + 68*x^4 + 125*x^3 + 24*x^2 + 29*x + 14, x^75 + 41*x^73 + 18*x^72 + 50*x^71 + 40*x^70 + 106*x^69 + 124*x^68 + 53*x^67 + 8*x^66 + 85*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 114*x^7 + 40*x^6 + 42*x^5 + 124*x^4 + 93*x^3 + 8*x^2 + 61*x + 34, x^75 + 41*x^73 + 78*x^72 + 18*x^71 + 24*x^70 + 10*x^69 + 68*x^68 + 85*x^67 + 56*x^66 + 53*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 82*x^7 + 24*x^6 + 74*x^5 + 68*x^4 + 125*x^3 + 56*x^2 + 29*x + 62, x^75 + 41*x^73 + 74*x^72 + 18*x^71 + 24*x^70 + 42*x^69 + 124*x^68 + 21*x^67 + 88*x^66 + 85*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 82*x^7 + 24*x^6 + 106*x^5 + 124*x^4 + 61*x^3 + 88*x^2 + 61*x + 42, x^75 + 41*x^73 + 6*x^72 + 98*x^71 + 88*x^70 + 122*x^69 + 84*x^68 + 5*x^67 + 120*x^66 + 69*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 34*x^7 + 88*x^6 + 58*x^5 + 84*x^4 + 45*x^3 + 120*x^2 + 45*x + 118, x^75 + 41*x^73 + 118*x^72 + 34*x^71 + 120*x^70 + 122*x^69 + 20*x^68 + 69*x^67 + 88*x^66 + 69*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 98*x^7 + 120*x^6 + 58*x^5 + 20*x^4 + 109*x^3 + 88*x^2 + 45*x + 70, x^75 + 41*x^73 + 18*x^72 + 2*x^71 + 120*x^70 + 58*x^69 + 12*x^68 + 37*x^67 + 120*x^66 + 69*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 66*x^7 + 120*x^6 + 122*x^5 + 12*x^4 + 77*x^3 + 120*x^2 + 45*x + 82, x^75 + 41*x^73 + 34*x^72 + 82*x^71 + 104*x^70 + 74*x^69 + 28*x^68 + 21*x^67 + 72*x^66 + 117*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 18*x^7 + 104*x^6 + 10*x^5 + 28*x^4 + 61*x^3 + 72*x^2 + 93*x + 114, x^75 + 41*x^73 + 122*x^72 + 114*x^71 + 88*x^70 + 74*x^69 + 92*x^68 + 53*x^67 + 24*x^66 + 53*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 50*x^7 + 88*x^6 + 10*x^5 + 92*x^4 + 93*x^3 + 24*x^2 + 29*x + 26, x^75 + 41*x^73 + 98*x^72 + 2*x^71 + 120*x^70 + 122*x^69 + 108*x^68 + 37*x^67 + 120*x^66 + 5*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 66*x^7 + 120*x^6 + 58*x^5 + 108*x^4 + 77*x^3 + 120*x^2 + 109*x + 34, x^75 + 41*x^73 + 122*x^72 + 66*x^71 + 72*x^70 + 26*x^69 + 12*x^68 + 37*x^67 + 104*x^66 + 37*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 2*x^7 + 72*x^6 + 90*x^5 + 12*x^4 + 77*x^3 + 104*x^2 + 13*x + 42, x^75 + 41*x^73 + 94*x^72 + 50*x^71 + 88*x^70 + 106*x^69 + 100*x^68 + 53*x^67 + 120*x^66 + 85*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 114*x^7 + 88*x^6 + 42*x^5 + 100*x^4 + 93*x^3 + 120*x^2 + 61*x + 14, x^75 + 41*x^73 + 38*x^72 + 2*x^71 + 120*x^70 + 90*x^69 + 116*x^68 + 101*x^67 + 88*x^66 + 101*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 66*x^7 + 120*x^6 + 26*x^5 + 116*x^4 + 13*x^3 + 88*x^2 + 77*x + 54, x^75 + 41*x^73 + 54*x^72 + 98*x^71 + 56*x^70 + 122*x^69 + 20*x^68 + 5*x^67 + 24*x^66 + 69*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 34*x^7 + 56*x^6 + 58*x^5 + 20*x^4 + 45*x^3 + 24*x^2 + 45*x + 6, x^75 + 41*x^73 + 2*x^72 + 82*x^71 + 72*x^70 + 74*x^69 + 60*x^68 + 21*x^67 + 104*x^66 + 117*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 18*x^7 + 72*x^6 + 10*x^5 + 60*x^4 + 61*x^3 + 104*x^2 + 93*x + 114, x^75 + 41*x^73 + 38*x^72 + 66*x^71 + 88*x^70 + 26*x^69 + 84*x^68 + 37*x^67 + 120*x^66 + 37*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 2*x^7 + 88*x^6 + 90*x^5 + 84*x^4 + 77*x^3 + 120*x^2 + 13*x + 86, x^75 + 41*x^73 + 58*x^72 + 66*x^71 + 8*x^70 + 90*x^69 + 12*x^68 + 37*x^67 + 40*x^66 + 101*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 2*x^7 + 8*x^6 + 26*x^5 + 12*x^4 + 77*x^3 + 40*x^2 + 77*x + 106, x^75 + 41*x^73 + 74*x^72 + 82*x^71 + 56*x^70 + 106*x^69 + 28*x^68 + 85*x^67 + 56*x^66 + 21*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 18*x^7 + 56*x^6 + 42*x^5 + 28*x^4 + 125*x^3 + 56*x^2 + 125*x + 10, x^75 + 41*x^73 + 18*x^72 + 98*x^71 + 88*x^70 + 90*x^69 + 44*x^68 + 69*x^67 + 24*x^66 + 37*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 34*x^7 + 88*x^6 + 26*x^5 + 44*x^4 + 109*x^3 + 24*x^2 + 13*x + 50, x^75 + 41*x^73 + 126*x^72 + 18*x^71 + 120*x^70 + 74*x^69 + 68*x^68 + 85*x^67 + 88*x^66 + 117*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 82*x^7 + 120*x^6 + 10*x^5 + 68*x^4 + 125*x^3 + 88*x^2 + 93*x + 14, x^75 + 41*x^73 + 2*x^72 + 66*x^71 + 120*x^70 + 58*x^69 + 44*x^68 + 101*x^67 + 120*x^66 + 69*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 2*x^7 + 120*x^6 + 122*x^5 + 44*x^4 + 13*x^3 + 120*x^2 + 45*x + 66, x^75 + 41*x^73 + 86*x^72 + 18*x^71 + 8*x^70 + 106*x^69 + 36*x^68 + 21*x^67 + 8*x^66 + 21*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 82*x^7 + 8*x^6 + 42*x^5 + 36*x^4 + 61*x^3 + 8*x^2 + 125*x + 22, x^75 + 41*x^73 + 42*x^72 + 82*x^71 + 120*x^70 + 106*x^69 + 28*x^68 + 85*x^67 + 120*x^66 + 21*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 18*x^7 + 120*x^6 + 42*x^5 + 28*x^4 + 125*x^3 + 120*x^2 + 125*x + 42, x^75 + 41*x^73 + 126*x^72 + 34*x^71 + 72*x^70 + 90*x^69 + 84*x^68 + 5*x^67 + 72*x^66 + 37*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 98*x^7 + 72*x^6 + 26*x^5 + 84*x^4 + 45*x^3 + 72*x^2 + 13*x + 62, x^75 + 41*x^73 + 118*x^72 + 18*x^71 + 40*x^70 + 42*x^69 + 68*x^68 + 21*x^67 + 104*x^66 + 85*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 82*x^7 + 40*x^6 + 106*x^5 + 68*x^4 + 61*x^3 + 104*x^2 + 61*x + 86, x^75 + 41*x^73 + 110*x^72 + 98*x^71 + 104*x^70 + 90*x^69 + 20*x^68 + 69*x^67 + 40*x^66 + 37*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 34*x^7 + 104*x^6 + 26*x^5 + 20*x^4 + 109*x^3 + 40*x^2 + 13*x + 14, x^75 + 41*x^73 + 86*x^72 + 50*x^71 + 8*x^70 + 10*x^69 + 36*x^68 + 117*x^67 + 8*x^66 + 117*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 114*x^7 + 8*x^6 + 74*x^5 + 36*x^4 + 29*x^3 + 8*x^2 + 93*x + 22, x^75 + 41*x^73 + 126*x^72 + 34*x^71 + 72*x^70 + 26*x^69 + 20*x^68 + 5*x^67 + 72*x^66 + 101*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 98*x^7 + 72*x^6 + 90*x^5 + 20*x^4 + 45*x^3 + 72*x^2 + 77*x + 126, x^75 + 41*x^73 + 2*x^72 + 34*x^71 + 88*x^70 + 90*x^69 + 76*x^68 + 5*x^67 + 24*x^66 + 37*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 98*x^7 + 88*x^6 + 26*x^5 + 76*x^4 + 45*x^3 + 24*x^2 + 13*x + 34, x^75 + 41*x^73 + 106*x^72 + 98*x^71 + 40*x^70 + 122*x^69 + 12*x^68 + 5*x^67 + 8*x^66 + 69*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 34*x^7 + 40*x^6 + 58*x^5 + 12*x^4 + 45*x^3 + 8*x^2 + 45*x + 58, x^75 + 41*x^73 + 78*x^72 + 114*x^71 + 24*x^70 + 42*x^69 + 4*x^68 + 117*x^67 + 56*x^66 + 21*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 50*x^7 + 24*x^6 + 106*x^5 + 4*x^4 + 29*x^3 + 56*x^2 + 125*x + 126, x^75 + 41*x^73 + 114*x^72 + 82*x^71 + 40*x^70 + 74*x^69 + 124*x^68 + 21*x^67 + 8*x^66 + 117*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 18*x^7 + 40*x^6 + 10*x^5 + 124*x^4 + 61*x^3 + 8*x^2 + 93*x + 66, x^75 + 41*x^73 + 94*x^72 + 82*x^71 + 24*x^70 + 74*x^69 + 100*x^68 + 21*x^67 + 56*x^66 + 117*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 18*x^7 + 24*x^6 + 10*x^5 + 100*x^4 + 61*x^3 + 56*x^2 + 93*x + 14, x^75 + 41*x^73 + 50*x^72 + 98*x^71 + 56*x^70 + 26*x^69 + 12*x^68 + 69*x^67 + 56*x^66 + 101*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 34*x^7 + 56*x^6 + 90*x^5 + 12*x^4 + 109*x^3 + 56*x^2 + 77*x + 50, x^75 + 41*x^73 + 14*x^72 + 34*x^71 + 104*x^70 + 90*x^69 + 20*x^68 + 5*x^67 + 40*x^66 + 37*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 98*x^7 + 104*x^6 + 26*x^5 + 20*x^4 + 45*x^3 + 40*x^2 + 13*x + 110, x^75 + 41*x^73 + 10*x^72 + 82*x^71 + 24*x^70 + 106*x^69 + 124*x^68 + 85*x^67 + 88*x^66 + 21*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 18*x^7 + 24*x^6 + 42*x^5 + 124*x^4 + 125*x^3 + 88*x^2 + 125*x + 106, x^75 + 41*x^73 + 22*x^72 + 50*x^71 + 8*x^70 + 74*x^69 + 100*x^68 + 117*x^67 + 8*x^66 + 53*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 114*x^7 + 8*x^6 + 10*x^5 + 100*x^4 + 29*x^3 + 8*x^2 + 29*x + 22, x^75 + 41*x^73 + 50*x^72 + 114*x^71 + 8*x^70 + 42*x^69 + 28*x^68 + 117*x^67 + 40*x^66 + 21*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 50*x^7 + 8*x^6 + 106*x^5 + 28*x^4 + 29*x^3 + 40*x^2 + 125*x + 98, x^75 + 41*x^73 + 6*x^72 + 98*x^71 + 88*x^70 + 58*x^69 + 20*x^68 + 5*x^67 + 120*x^66 + 5*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 34*x^7 + 88*x^6 + 122*x^5 + 20*x^4 + 45*x^3 + 120*x^2 + 109*x + 54, x^75 + 41*x^73 + 42*x^72 + 18*x^71 + 56*x^70 + 106*x^69 + 28*x^68 + 21*x^67 + 56*x^66 + 21*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 82*x^7 + 56*x^6 + 42*x^5 + 28*x^4 + 61*x^3 + 56*x^2 + 125*x + 42, x^75 + 41*x^73 + 102*x^72 + 114*x^71 + 104*x^70 + 74*x^69 + 36*x^68 + 53*x^67 + 40*x^66 + 53*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 50*x^7 + 104*x^6 + 10*x^5 + 36*x^4 + 93*x^3 + 40*x^2 + 29*x + 6, x^75 + 41*x^73 + 58*x^72 + 34*x^71 + 40*x^70 + 58*x^69 + 44*x^68 + 69*x^67 + 8*x^66 + 5*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 98*x^7 + 40*x^6 + 122*x^5 + 44*x^4 + 109*x^3 + 8*x^2 + 109*x + 74, x^75 + 41*x^73 + 102*x^72 + 18*x^71 + 40*x^70 + 106*x^69 + 100*x^68 + 21*x^67 + 104*x^66 + 21*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 82*x^7 + 40*x^6 + 42*x^5 + 100*x^4 + 61*x^3 + 104*x^2 + 125*x + 70, x^75 + 41*x^73 + 6*x^72 + 50*x^71 + 40*x^70 + 10*x^69 + 36*x^68 + 117*x^67 + 104*x^66 + 117*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 114*x^7 + 40*x^6 + 74*x^5 + 36*x^4 + 29*x^3 + 104*x^2 + 93*x + 102, x^75 + 41*x^73 + 50*x^72 + 18*x^71 + 40*x^70 + 10*x^69 + 124*x^68 + 85*x^67 + 8*x^66 + 53*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 82*x^7 + 40*x^6 + 74*x^5 + 124*x^4 + 125*x^3 + 8*x^2 + 29*x + 2, x^75 + 41*x^73 + 114*x^72 + 18*x^71 + 72*x^70 + 10*x^69 + 28*x^68 + 85*x^67 + 104*x^66 + 53*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 82*x^7 + 72*x^6 + 74*x^5 + 28*x^4 + 125*x^3 + 104*x^2 + 29*x + 34, x^75 + 41*x^73 + 66*x^72 + 34*x^71 + 88*x^70 + 90*x^69 + 76*x^68 + 5*x^67 + 24*x^66 + 37*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 98*x^7 + 88*x^6 + 26*x^5 + 76*x^4 + 45*x^3 + 24*x^2 + 13*x + 98, x^75 + 41*x^73 + 86*x^72 + 50*x^71 + 72*x^70 + 74*x^69 + 36*x^68 + 117*x^67 + 72*x^66 + 53*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 114*x^7 + 72*x^6 + 10*x^5 + 36*x^4 + 29*x^3 + 72*x^2 + 29*x + 22, x^75 + 41*x^73 + 126*x^72 + 98*x^71 + 8*x^70 + 90*x^69 + 84*x^68 + 69*x^67 + 8*x^66 + 37*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 34*x^7 + 8*x^6 + 26*x^5 + 84*x^4 + 109*x^3 + 8*x^2 + 13*x + 62, x^75 + 41*x^73 + 38*x^72 + 34*x^71 + 120*x^70 + 122*x^69 + 116*x^68 + 69*x^67 + 88*x^66 + 69*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 98*x^7 + 120*x^6 + 58*x^5 + 116*x^4 + 109*x^3 + 88*x^2 + 45*x + 54, x^75 + 41*x^73 + 18*x^72 + 114*x^71 + 72*x^70 + 106*x^69 + 92*x^68 + 117*x^67 + 104*x^66 + 85*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 50*x^7 + 72*x^6 + 42*x^5 + 92*x^4 + 29*x^3 + 104*x^2 + 61*x + 66, x^75 + 41*x^73 + 98*x^72 + 50*x^71 + 8*x^70 + 106*x^69 + 124*x^68 + 53*x^67 + 40*x^66 + 85*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 114*x^7 + 8*x^6 + 42*x^5 + 124*x^4 + 93*x^3 + 40*x^2 + 61*x + 82, x^75 + 41*x^73 + 22*x^72 + 50*x^71 + 40*x^70 + 74*x^69 + 4*x^68 + 117*x^67 + 104*x^66 + 53*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 114*x^7 + 40*x^6 + 10*x^5 + 4*x^4 + 29*x^3 + 104*x^2 + 29*x + 118, x^75 + 41*x^73 + 114*x^72 + 66*x^71 + 88*x^70 + 122*x^69 + 44*x^68 + 101*x^67 + 24*x^66 + 5*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 2*x^7 + 88*x^6 + 58*x^5 + 44*x^4 + 13*x^3 + 24*x^2 + 109*x + 82, x^75 + 41*x^73 + 86*x^72 + 82*x^71 + 40*x^70 + 42*x^69 + 68*x^68 + 85*x^67 + 104*x^66 + 85*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 18*x^7 + 40*x^6 + 106*x^5 + 68*x^4 + 125*x^3 + 104*x^2 + 61*x + 118, x^75 + 41*x^73 + 94*x^72 + 114*x^71 + 88*x^70 + 42*x^69 + 100*x^68 + 117*x^67 + 120*x^66 + 21*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 50*x^7 + 88*x^6 + 106*x^5 + 100*x^4 + 29*x^3 + 120*x^2 + 125*x + 14, x^75 + 41*x^73 + 126*x^72 + 98*x^71 + 8*x^70 + 26*x^69 + 20*x^68 + 69*x^67 + 8*x^66 + 101*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 34*x^7 + 8*x^6 + 90*x^5 + 20*x^4 + 109*x^3 + 8*x^2 + 77*x + 126, x^75 + 41*x^73 + 50*x^72 + 34*x^71 + 120*x^70 + 90*x^69 + 76*x^68 + 5*x^67 + 120*x^66 + 37*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 98*x^7 + 120*x^6 + 26*x^5 + 76*x^4 + 45*x^3 + 120*x^2 + 13*x + 114, x^75 + 41*x^73 + 42*x^72 + 34*x^71 + 72*x^70 + 122*x^69 + 108*x^68 + 69*x^67 + 104*x^66 + 69*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 98*x^7 + 72*x^6 + 58*x^5 + 108*x^4 + 109*x^3 + 104*x^2 + 45*x + 26, x^75 + 41*x^73 + 42*x^72 + 98*x^71 + 72*x^70 + 122*x^69 + 44*x^68 + 5*x^67 + 104*x^66 + 69*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 34*x^7 + 72*x^6 + 58*x^5 + 44*x^4 + 45*x^3 + 104*x^2 + 45*x + 90, x^75 + 41*x^73 + 90*x^72 + 34*x^71 + 104*x^70 + 122*x^69 + 108*x^68 + 69*x^67 + 72*x^66 + 69*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 98*x^7 + 104*x^6 + 58*x^5 + 108*x^4 + 109*x^3 + 72*x^2 + 45*x + 106, x^75 + 41*x^73 + 6*x^72 + 82*x^71 + 40*x^70 + 42*x^69 + 36*x^68 + 85*x^67 + 104*x^66 + 85*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 18*x^7 + 40*x^6 + 106*x^5 + 36*x^4 + 125*x^3 + 104*x^2 + 61*x + 102, x^75 + 41*x^73 + 14*x^72 + 50*x^71 + 56*x^70 + 42*x^69 + 100*x^68 + 53*x^67 + 24*x^66 + 21*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 114*x^7 + 56*x^6 + 106*x^5 + 100*x^4 + 93*x^3 + 24*x^2 + 125*x + 94, x^75 + 41*x^73 + 2*x^72 + 98*x^71 + 120*x^70 + 26*x^69 + 108*x^68 + 69*x^67 + 120*x^66 + 101*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 34*x^7 + 120*x^6 + 90*x^5 + 108*x^4 + 109*x^3 + 120*x^2 + 77*x + 2, x^75 + 41*x^73 + 94*x^72 + 18*x^71 + 24*x^70 + 74*x^69 + 36*x^68 + 85*x^67 + 56*x^66 + 117*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 82*x^7 + 24*x^6 + 10*x^5 + 36*x^4 + 125*x^3 + 56*x^2 + 93*x + 78, x^75 + 41*x^73 + 2*x^72 + 34*x^71 + 56*x^70 + 90*x^69 + 44*x^68 + 5*x^67 + 56*x^66 + 37*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 98*x^7 + 56*x^6 + 26*x^5 + 44*x^4 + 45*x^3 + 56*x^2 + 13*x + 66, x^75 + 41*x^73 + 18*x^72 + 82*x^71 + 8*x^70 + 74*x^69 + 28*x^68 + 21*x^67 + 40*x^66 + 117*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 18*x^7 + 8*x^6 + 10*x^5 + 28*x^4 + 61*x^3 + 40*x^2 + 93*x + 2, x^75 + 41*x^73 + 66*x^72 + 34*x^71 + 24*x^70 + 90*x^69 + 12*x^68 + 5*x^67 + 88*x^66 + 37*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 98*x^7 + 24*x^6 + 26*x^5 + 12*x^4 + 45*x^3 + 88*x^2 + 13*x + 34, x^75 + 41*x^73 + 62*x^72 + 82*x^71 + 56*x^70 + 74*x^69 + 68*x^68 + 21*x^67 + 24*x^66 + 117*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 18*x^7 + 56*x^6 + 10*x^5 + 68*x^4 + 61*x^3 + 24*x^2 + 93*x + 78, x^75 + 41*x^73 + 110*x^72 + 66*x^71 + 104*x^70 + 58*x^69 + 20*x^68 + 101*x^67 + 40*x^66 + 69*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 2*x^7 + 104*x^6 + 122*x^5 + 20*x^4 + 13*x^3 + 40*x^2 + 45*x + 14, x^75 + 41*x^73 + 2*x^72 + 66*x^71 + 56*x^70 + 58*x^69 + 108*x^68 + 101*x^67 + 56*x^66 + 69*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 2*x^7 + 56*x^6 + 122*x^5 + 108*x^4 + 13*x^3 + 56*x^2 + 45*x + 2, x^75 + 41*x^73 + 122*x^72 + 82*x^71 + 120*x^70 + 42*x^69 + 124*x^68 + 85*x^67 + 120*x^66 + 85*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 18*x^7 + 120*x^6 + 106*x^5 + 124*x^4 + 125*x^3 + 120*x^2 + 61*x + 122, x^75 + 41*x^73 + 62*x^72 + 2*x^71 + 72*x^70 + 122*x^69 + 20*x^68 + 37*x^67 + 72*x^66 + 5*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 66*x^7 + 72*x^6 + 58*x^5 + 20*x^4 + 77*x^3 + 72*x^2 + 109*x + 62, x^75 + 41*x^73 + 14*x^72 + 66*x^71 + 40*x^70 + 58*x^69 + 20*x^68 + 101*x^67 + 104*x^66 + 69*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 2*x^7 + 40*x^6 + 122*x^5 + 20*x^4 + 13*x^3 + 104*x^2 + 45*x + 110, x^75 + 41*x^73 + 46*x^72 + 2*x^71 + 40*x^70 + 58*x^69 + 20*x^68 + 37*x^67 + 104*x^66 + 69*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 66*x^7 + 40*x^6 + 122*x^5 + 20*x^4 + 77*x^3 + 104*x^2 + 45*x + 78, x^75 + 41*x^73 + 78*x^72 + 2*x^71 + 72*x^70 + 122*x^69 + 52*x^68 + 37*x^67 + 72*x^66 + 5*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 66*x^7 + 72*x^6 + 58*x^5 + 52*x^4 + 77*x^3 + 72*x^2 + 109*x + 14, x^75 + 41*x^73 + 82*x^72 + 66*x^71 + 56*x^70 + 58*x^69 + 12*x^68 + 101*x^67 + 56*x^66 + 69*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 2*x^7 + 56*x^6 + 122*x^5 + 12*x^4 + 13*x^3 + 56*x^2 + 45*x + 18, x^75 + 41*x^73 + 54*x^72 + 34*x^71 + 120*x^70 + 122*x^69 + 20*x^68 + 69*x^67 + 88*x^66 + 69*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 98*x^7 + 120*x^6 + 58*x^5 + 20*x^4 + 109*x^3 + 88*x^2 + 45*x + 6, x^75 + 41*x^73 + 106*x^72 + 34*x^71 + 40*x^70 + 122*x^69 + 76*x^68 + 69*x^67 + 8*x^66 + 69*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 98*x^7 + 40*x^6 + 58*x^5 + 76*x^4 + 109*x^3 + 8*x^2 + 45*x + 122, x^75 + 41*x^73 + 58*x^72 + 82*x^71 + 120*x^70 + 42*x^69 + 124*x^68 + 85*x^67 + 120*x^66 + 85*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 18*x^7 + 120*x^6 + 106*x^5 + 124*x^4 + 125*x^3 + 120*x^2 + 61*x + 58, x^75 + 41*x^73 + 106*x^72 + 114*x^71 + 88*x^70 + 10*x^69 + 124*x^68 + 53*x^67 + 24*x^66 + 117*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 50*x^7 + 88*x^6 + 74*x^5 + 124*x^4 + 93*x^3 + 24*x^2 + 93*x + 10, x^75 + 41*x^73 + 54*x^72 + 2*x^71 + 24*x^70 + 90*x^69 + 52*x^68 + 101*x^67 + 56*x^66 + 101*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 66*x^7 + 24*x^6 + 26*x^5 + 52*x^4 + 13*x^3 + 56*x^2 + 77*x + 102, x^75 + 41*x^73 + 122*x^72 + 114*x^71 + 120*x^70 + 10*x^69 + 60*x^68 + 53*x^67 + 120*x^66 + 117*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 50*x^7 + 120*x^6 + 74*x^5 + 60*x^4 + 93*x^3 + 120*x^2 + 93*x + 58, x^75 + 41*x^73 + 50*x^72 + 2*x^71 + 56*x^70 + 122*x^69 + 76*x^68 + 37*x^67 + 56*x^66 + 5*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 66*x^7 + 56*x^6 + 58*x^5 + 76*x^4 + 77*x^3 + 56*x^2 + 109*x + 114, x^75 + 41*x^73 + 22*x^72 + 114*x^71 + 40*x^70 + 74*x^69 + 68*x^68 + 53*x^67 + 104*x^66 + 53*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 50*x^7 + 40*x^6 + 10*x^5 + 68*x^4 + 93*x^3 + 104*x^2 + 29*x + 54, x^75 + 41*x^73 + 86*x^72 + 82*x^71 + 104*x^70 + 106*x^69 + 68*x^68 + 85*x^67 + 40*x^66 + 21*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 18*x^7 + 104*x^6 + 42*x^5 + 68*x^4 + 125*x^3 + 40*x^2 + 125*x + 118, x^75 + 41*x^73 + 62*x^72 + 66*x^71 + 8*x^70 + 58*x^69 + 84*x^68 + 101*x^67 + 8*x^66 + 69*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 2*x^7 + 8*x^6 + 122*x^5 + 84*x^4 + 13*x^3 + 8*x^2 + 45*x + 126, x^75 + 41*x^73 + 34*x^72 + 66*x^71 + 24*x^70 + 58*x^69 + 12*x^68 + 101*x^67 + 88*x^66 + 69*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 2*x^7 + 24*x^6 + 122*x^5 + 12*x^4 + 13*x^3 + 88*x^2 + 45*x + 66, x^75 + 41*x^73 + 62*x^72 + 114*x^71 + 120*x^70 + 42*x^69 + 68*x^68 + 117*x^67 + 88*x^66 + 21*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 50*x^7 + 120*x^6 + 106*x^5 + 68*x^4 + 29*x^3 + 88*x^2 + 125*x + 78, x^75 + 41*x^73 + 126*x^72 + 50*x^71 + 120*x^70 + 106*x^69 + 68*x^68 + 53*x^67 + 88*x^66 + 85*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 114*x^7 + 120*x^6 + 42*x^5 + 68*x^4 + 93*x^3 + 88*x^2 + 61*x + 14, x^75 + 41*x^73 + 86*x^72 + 18*x^71 + 40*x^70 + 42*x^69 + 4*x^68 + 21*x^67 + 104*x^66 + 85*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 82*x^7 + 40*x^6 + 106*x^5 + 4*x^4 + 61*x^3 + 104*x^2 + 61*x + 54, x^75 + 41*x^73 + 22*x^72 + 18*x^71 + 72*x^70 + 42*x^69 + 36*x^68 + 21*x^67 + 72*x^66 + 85*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 82*x^7 + 72*x^6 + 106*x^5 + 36*x^4 + 61*x^3 + 72*x^2 + 61*x + 86, x^75 + 41*x^73 + 54*x^72 + 34*x^71 + 56*x^70 + 122*x^69 + 84*x^68 + 69*x^67 + 24*x^66 + 69*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 98*x^7 + 56*x^6 + 58*x^5 + 84*x^4 + 109*x^3 + 24*x^2 + 45*x + 70, x^75 + 41*x^73 + 54*x^72 + 66*x^71 + 88*x^70 + 90*x^69 + 52*x^68 + 37*x^67 + 120*x^66 + 101*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 2*x^7 + 88*x^6 + 26*x^5 + 52*x^4 + 77*x^3 + 120*x^2 + 77*x + 102, x^75 + 41*x^73 + 110*x^72 + 114*x^71 + 56*x^70 + 42*x^69 + 100*x^68 + 117*x^67 + 24*x^66 + 21*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 50*x^7 + 56*x^6 + 106*x^5 + 100*x^4 + 29*x^3 + 24*x^2 + 125*x + 126, x^75 + 41*x^73 + 38*x^72 + 82*x^71 + 104*x^70 + 106*x^69 + 100*x^68 + 85*x^67 + 40*x^66 + 21*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 18*x^7 + 104*x^6 + 42*x^5 + 100*x^4 + 125*x^3 + 40*x^2 + 125*x + 6, x^75 + 41*x^73 + 98*x^72 + 114*x^71 + 40*x^70 + 106*x^69 + 92*x^68 + 117*x^67 + 8*x^66 + 85*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 50*x^7 + 40*x^6 + 42*x^5 + 92*x^4 + 29*x^3 + 8*x^2 + 61*x + 114, x^75 + 41*x^73 + 110*x^72 + 114*x^71 + 120*x^70 + 106*x^69 + 100*x^68 + 117*x^67 + 88*x^66 + 85*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 50*x^7 + 120*x^6 + 42*x^5 + 100*x^4 + 29*x^3 + 88*x^2 + 61*x + 126, x^75 + 41*x^73 + 114*x^72 + 34*x^71 + 88*x^70 + 90*x^69 + 44*x^68 + 5*x^67 + 24*x^66 + 37*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 98*x^7 + 88*x^6 + 26*x^5 + 44*x^4 + 45*x^3 + 24*x^2 + 13*x + 82, x^75 + 41*x^73 + 122*x^72 + 98*x^71 + 40*x^70 + 58*x^69 + 108*x^68 + 5*x^67 + 8*x^66 + 5*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 34*x^7 + 40*x^6 + 122*x^5 + 108*x^4 + 45*x^3 + 8*x^2 + 109*x + 74, x^75 + 41*x^73 + 38*x^72 + 2*x^71 + 24*x^70 + 26*x^69 + 84*x^68 + 101*x^67 + 56*x^66 + 37*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 66*x^7 + 24*x^6 + 90*x^5 + 84*x^4 + 13*x^3 + 56*x^2 + 13*x + 86, x^75 + 41*x^73 + 10*x^72 + 18*x^71 + 88*x^70 + 42*x^69 + 60*x^68 + 21*x^67 + 24*x^66 + 85*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 82*x^7 + 88*x^6 + 106*x^5 + 60*x^4 + 61*x^3 + 24*x^2 + 61*x + 42, x^75 + 41*x^73 + 106*x^72 + 98*x^71 + 72*x^70 + 58*x^69 + 108*x^68 + 5*x^67 + 104*x^66 + 5*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 34*x^7 + 72*x^6 + 122*x^5 + 108*x^4 + 45*x^3 + 104*x^2 + 109*x + 90, x^75 + 41*x^73 + 58*x^72 + 2*x^71 + 8*x^70 + 90*x^69 + 76*x^68 + 101*x^67 + 40*x^66 + 101*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 66*x^7 + 8*x^6 + 26*x^5 + 76*x^4 + 13*x^3 + 40*x^2 + 77*x + 42, x^75 + 41*x^73 + 82*x^72 + 82*x^71 + 40*x^70 + 10*x^69 + 124*x^68 + 21*x^67 + 8*x^66 + 53*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 18*x^7 + 40*x^6 + 74*x^5 + 124*x^4 + 61*x^3 + 8*x^2 + 29*x + 98, x^75 + 41*x^73 + 62*x^72 + 18*x^71 + 120*x^70 + 10*x^69 + 4*x^68 + 85*x^67 + 88*x^66 + 53*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 82*x^7 + 120*x^6 + 74*x^5 + 4*x^4 + 125*x^3 + 88*x^2 + 29*x + 14, x^75 + 41*x^73 + 50*x^72 + 114*x^71 + 72*x^70 + 106*x^69 + 28*x^68 + 117*x^67 + 104*x^66 + 85*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 50*x^7 + 72*x^6 + 42*x^5 + 28*x^4 + 29*x^3 + 104*x^2 + 61*x + 98, x^75 + 41*x^73 + 94*x^72 + 2*x^71 + 8*x^70 + 58*x^69 + 84*x^68 + 37*x^67 + 8*x^66 + 69*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 66*x^7 + 8*x^6 + 122*x^5 + 84*x^4 + 77*x^3 + 8*x^2 + 45*x + 94, x^75 + 41*x^73 + 106*x^72 + 98*x^71 + 104*x^70 + 58*x^69 + 12*x^68 + 5*x^67 + 72*x^66 + 5*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 34*x^7 + 104*x^6 + 122*x^5 + 12*x^4 + 45*x^3 + 72*x^2 + 109*x + 58, x^75 + 41*x^73 + 74*x^72 + 18*x^71 + 120*x^70 + 106*x^69 + 28*x^68 + 21*x^67 + 120*x^66 + 21*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 82*x^7 + 120*x^6 + 42*x^5 + 28*x^4 + 61*x^3 + 120*x^2 + 125*x + 10, x^75 + 41*x^73 + 102*x^72 + 98*x^71 + 24*x^70 + 122*x^69 + 84*x^68 + 5*x^67 + 56*x^66 + 69*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 34*x^7 + 24*x^6 + 58*x^5 + 84*x^4 + 45*x^3 + 56*x^2 + 45*x + 22, x^75 + 41*x^73 + 14*x^72 + 114*x^71 + 24*x^70 + 42*x^69 + 4*x^68 + 117*x^67 + 56*x^66 + 21*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 50*x^7 + 24*x^6 + 106*x^5 + 4*x^4 + 29*x^3 + 56*x^2 + 125*x + 62, x^75 + 41*x^73 + 30*x^72 + 34*x^71 + 40*x^70 + 90*x^69 + 116*x^68 + 5*x^67 + 104*x^66 + 37*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 98*x^7 + 40*x^6 + 26*x^5 + 116*x^4 + 45*x^3 + 104*x^2 + 13*x + 126, x^75 + 41*x^73 + 26*x^72 + 114*x^71 + 88*x^70 + 74*x^69 + 28*x^68 + 53*x^67 + 24*x^66 + 53*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 50*x^7 + 88*x^6 + 10*x^5 + 28*x^4 + 93*x^3 + 24*x^2 + 29*x + 58, x^75 + 41*x^73 + 78*x^72 + 50*x^71 + 24*x^70 + 106*x^69 + 4*x^68 + 53*x^67 + 56*x^66 + 85*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 114*x^7 + 24*x^6 + 42*x^5 + 4*x^4 + 93*x^3 + 56*x^2 + 61*x + 126, x^75 + 41*x^73 + 94*x^72 + 82*x^71 + 120*x^70 + 10*x^69 + 4*x^68 + 21*x^67 + 88*x^66 + 53*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 18*x^7 + 120*x^6 + 74*x^5 + 4*x^4 + 61*x^3 + 88*x^2 + 29*x + 110, x^75 + 41*x^73 + 74*x^72 + 50*x^71 + 24*x^70 + 74*x^69 + 124*x^68 + 117*x^67 + 88*x^66 + 53*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 114*x^7 + 24*x^6 + 10*x^5 + 124*x^4 + 29*x^3 + 88*x^2 + 29*x + 42, x^75 + 41*x^73 + 10*x^72 + 18*x^71 + 56*x^70 + 106*x^69 + 92*x^68 + 21*x^67 + 56*x^66 + 21*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 82*x^7 + 56*x^6 + 42*x^5 + 92*x^4 + 61*x^3 + 56*x^2 + 125*x + 10, x^75 + 41*x^73 + 14*x^72 + 34*x^71 + 40*x^70 + 90*x^69 + 84*x^68 + 5*x^67 + 104*x^66 + 37*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 98*x^7 + 40*x^6 + 26*x^5 + 84*x^4 + 45*x^3 + 104*x^2 + 13*x + 46, x^75 + 41*x^73 + 18*x^72 + 34*x^71 + 56*x^70 + 90*x^69 + 76*x^68 + 5*x^67 + 56*x^66 + 37*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 98*x^7 + 56*x^6 + 26*x^5 + 76*x^4 + 45*x^3 + 56*x^2 + 13*x + 18, x^75 + 41*x^73 + 2*x^72 + 2*x^71 + 24*x^70 + 58*x^69 + 12*x^68 + 37*x^67 + 88*x^66 + 69*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 66*x^7 + 24*x^6 + 122*x^5 + 12*x^4 + 77*x^3 + 88*x^2 + 45*x + 98, x^75 + 41*x^73 + 10*x^72 + 18*x^71 + 88*x^70 + 106*x^69 + 124*x^68 + 21*x^67 + 24*x^66 + 21*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 82*x^7 + 88*x^6 + 42*x^5 + 124*x^4 + 61*x^3 + 24*x^2 + 125*x + 106, x^75 + 41*x^73 + 90*x^72 + 66*x^71 + 72*x^70 + 26*x^69 + 76*x^68 + 37*x^67 + 104*x^66 + 37*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 2*x^7 + 72*x^6 + 90*x^5 + 76*x^4 + 77*x^3 + 104*x^2 + 13*x + 10, x^75 + 41*x^73 + 122*x^72 + 82*x^71 + 56*x^70 + 42*x^69 + 60*x^68 + 85*x^67 + 56*x^66 + 85*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 18*x^7 + 56*x^6 + 106*x^5 + 60*x^4 + 125*x^3 + 56*x^2 + 61*x + 58, x^75 + 41*x^73 + 78*x^72 + 18*x^71 + 56*x^70 + 10*x^69 + 100*x^68 + 85*x^67 + 24*x^66 + 53*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 82*x^7 + 56*x^6 + 74*x^5 + 100*x^4 + 125*x^3 + 24*x^2 + 29*x + 30, x^75 + 41*x^73 + 78*x^72 + 50*x^71 + 24*x^70 + 42*x^69 + 68*x^68 + 53*x^67 + 56*x^66 + 21*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 114*x^7 + 24*x^6 + 106*x^5 + 68*x^4 + 93*x^3 + 56*x^2 + 125*x + 62, x^75 + 41*x^73 + 46*x^72 + 2*x^71 + 8*x^70 + 58*x^69 + 116*x^68 + 37*x^67 + 8*x^66 + 69*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 66*x^7 + 8*x^6 + 122*x^5 + 116*x^4 + 77*x^3 + 8*x^2 + 45*x + 110, x^75 + 41*x^73 + 70*x^72 + 82*x^71 + 104*x^70 + 42*x^69 + 100*x^68 + 85*x^67 + 40*x^66 + 85*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 18*x^7 + 104*x^6 + 106*x^5 + 100*x^4 + 125*x^3 + 40*x^2 + 61*x + 102, x^75 + 41*x^73 + 94*x^72 + 82*x^71 + 56*x^70 + 74*x^69 + 4*x^68 + 21*x^67 + 24*x^66 + 117*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 18*x^7 + 56*x^6 + 10*x^5 + 4*x^4 + 61*x^3 + 24*x^2 + 93*x + 110, x^75 + 41*x^73 + 18*x^72 + 2*x^71 + 120*x^70 + 122*x^69 + 76*x^68 + 37*x^67 + 120*x^66 + 5*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 66*x^7 + 120*x^6 + 58*x^5 + 76*x^4 + 77*x^3 + 120*x^2 + 109*x + 18, x^75 + 41*x^73 + 38*x^72 + 2*x^71 + 120*x^70 + 26*x^69 + 52*x^68 + 101*x^67 + 88*x^66 + 37*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 66*x^7 + 120*x^6 + 90*x^5 + 52*x^4 + 13*x^3 + 88*x^2 + 13*x + 118, x^75 + 41*x^73 + 98*x^72 + 34*x^71 + 56*x^70 + 90*x^69 + 108*x^68 + 5*x^67 + 56*x^66 + 37*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 98*x^7 + 56*x^6 + 26*x^5 + 108*x^4 + 45*x^3 + 56*x^2 + 13*x + 34, x^75 + 41*x^73 + 94*x^72 + 18*x^71 + 88*x^70 + 74*x^69 + 100*x^68 + 85*x^67 + 120*x^66 + 117*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 82*x^7 + 88*x^6 + 10*x^5 + 100*x^4 + 125*x^3 + 120*x^2 + 93*x + 14, x^75 + 41*x^73 + 54*x^72 + 34*x^71 + 24*x^70 + 122*x^69 + 52*x^68 + 69*x^67 + 56*x^66 + 69*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 98*x^7 + 24*x^6 + 58*x^5 + 52*x^4 + 109*x^3 + 56*x^2 + 45*x + 102, x^75 + 41*x^73 + 118*x^72 + 34*x^71 + 56*x^70 + 122*x^69 + 84*x^68 + 69*x^67 + 24*x^66 + 69*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 98*x^7 + 56*x^6 + 58*x^5 + 84*x^4 + 109*x^3 + 24*x^2 + 45*x + 6, x^75 + 41*x^73 + 30*x^72 + 82*x^71 + 24*x^70 + 74*x^69 + 100*x^68 + 21*x^67 + 56*x^66 + 117*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 18*x^7 + 24*x^6 + 10*x^5 + 100*x^4 + 61*x^3 + 56*x^2 + 93*x + 78, x^75 + 41*x^73 + 70*x^72 + 66*x^71 + 24*x^70 + 26*x^69 + 84*x^68 + 37*x^67 + 56*x^66 + 37*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 2*x^7 + 24*x^6 + 90*x^5 + 84*x^4 + 77*x^3 + 56*x^2 + 13*x + 54, x^75 + 41*x^73 + 10*x^72 + 50*x^71 + 24*x^70 + 74*x^69 + 124*x^68 + 117*x^67 + 88*x^66 + 53*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 114*x^7 + 24*x^6 + 10*x^5 + 124*x^4 + 29*x^3 + 88*x^2 + 29*x + 106, x^75 + 41*x^73 + 6*x^72 + 18*x^71 + 104*x^70 + 106*x^69 + 100*x^68 + 21*x^67 + 40*x^66 + 21*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 82*x^7 + 104*x^6 + 42*x^5 + 100*x^4 + 61*x^3 + 40*x^2 + 125*x + 38, x^75 + 41*x^73 + 98*x^72 + 82*x^71 + 72*x^70 + 10*x^69 + 60*x^68 + 21*x^67 + 104*x^66 + 53*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 18*x^7 + 72*x^6 + 74*x^5 + 60*x^4 + 61*x^3 + 104*x^2 + 29*x + 18, x^75 + 41*x^73 + 42*x^72 + 18*x^71 + 24*x^70 + 106*x^69 + 124*x^68 + 21*x^67 + 88*x^66 + 21*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 82*x^7 + 24*x^6 + 42*x^5 + 124*x^4 + 61*x^3 + 88*x^2 + 125*x + 74, x^75 + 41*x^73 + 126*x^72 + 2*x^71 + 40*x^70 + 58*x^69 + 52*x^68 + 37*x^67 + 104*x^66 + 69*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 66*x^7 + 40*x^6 + 122*x^5 + 52*x^4 + 77*x^3 + 104*x^2 + 45*x + 94, x^75 + 41*x^73 + 2*x^72 + 82*x^71 + 40*x^70 + 74*x^69 + 28*x^68 + 21*x^67 + 8*x^66 + 117*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 18*x^7 + 40*x^6 + 10*x^5 + 28*x^4 + 61*x^3 + 8*x^2 + 93*x + 18, x^75 + 41*x^73 + 66*x^72 + 34*x^71 + 120*x^70 + 26*x^69 + 44*x^68 + 5*x^67 + 120*x^66 + 101*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 98*x^7 + 120*x^6 + 90*x^5 + 44*x^4 + 45*x^3 + 120*x^2 + 77*x + 2, x^75 + 41*x^73 + 70*x^72 + 114*x^71 + 40*x^70 + 74*x^69 + 36*x^68 + 53*x^67 + 104*x^66 + 53*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 50*x^7 + 40*x^6 + 10*x^5 + 36*x^4 + 93*x^3 + 104*x^2 + 29*x + 38, x^75 + 41*x^73 + 94*x^72 + 114*x^71 + 120*x^70 + 42*x^69 + 4*x^68 + 117*x^67 + 88*x^66 + 21*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 50*x^7 + 120*x^6 + 106*x^5 + 4*x^4 + 29*x^3 + 88*x^2 + 125*x + 110, x^75 + 41*x^73 + 46*x^72 + 50*x^71 + 120*x^70 + 42*x^69 + 100*x^68 + 53*x^67 + 88*x^66 + 21*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 114*x^7 + 120*x^6 + 106*x^5 + 100*x^4 + 93*x^3 + 88*x^2 + 125*x + 62, x^75 + 41*x^73 + 110*x^72 + 18*x^71 + 88*x^70 + 74*x^69 + 4*x^68 + 85*x^67 + 120*x^66 + 117*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 82*x^7 + 88*x^6 + 10*x^5 + 4*x^4 + 125*x^3 + 120*x^2 + 93*x + 94, x^75 + 41*x^73 + 10*x^72 + 66*x^71 + 72*x^70 + 26*x^69 + 44*x^68 + 37*x^67 + 104*x^66 + 37*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 2*x^7 + 72*x^6 + 90*x^5 + 44*x^4 + 77*x^3 + 104*x^2 + 13*x + 122, x^75 + 41*x^73 + 62*x^72 + 66*x^71 + 8*x^70 + 122*x^69 + 20*x^68 + 101*x^67 + 8*x^66 + 5*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 2*x^7 + 8*x^6 + 58*x^5 + 20*x^4 + 13*x^3 + 8*x^2 + 109*x + 62, x^75 + 41*x^73 + 10*x^72 + 114*x^71 + 88*x^70 + 10*x^69 + 60*x^68 + 53*x^67 + 24*x^66 + 117*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 50*x^7 + 88*x^6 + 74*x^5 + 60*x^4 + 93*x^3 + 24*x^2 + 93*x + 42, x^75 + 41*x^73 + 42*x^72 + 98*x^71 + 8*x^70 + 122*x^69 + 108*x^68 + 5*x^67 + 40*x^66 + 69*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 34*x^7 + 8*x^6 + 58*x^5 + 108*x^4 + 45*x^3 + 40*x^2 + 45*x + 26, x^75 + 41*x^73 + 82*x^72 + 114*x^71 + 104*x^70 + 106*x^69 + 124*x^68 + 117*x^67 + 72*x^66 + 85*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 50*x^7 + 104*x^6 + 42*x^5 + 124*x^4 + 29*x^3 + 72*x^2 + 61*x + 98, x^75 + 41*x^73 + 122*x^72 + 34*x^71 + 8*x^70 + 122*x^69 + 76*x^68 + 69*x^67 + 40*x^66 + 69*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 98*x^7 + 8*x^6 + 58*x^5 + 76*x^4 + 109*x^3 + 40*x^2 + 45*x + 106, x^75 + 41*x^73 + 34*x^72 + 98*x^71 + 120*x^70 + 26*x^69 + 44*x^68 + 69*x^67 + 120*x^66 + 101*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 34*x^7 + 120*x^6 + 90*x^5 + 44*x^4 + 109*x^3 + 120*x^2 + 77*x + 34, x^75 + 41*x^73 + 114*x^72 + 2*x^71 + 88*x^70 + 122*x^69 + 108*x^68 + 37*x^67 + 24*x^66 + 5*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 66*x^7 + 88*x^6 + 58*x^5 + 108*x^4 + 77*x^3 + 24*x^2 + 109*x + 18, x^75 + 41*x^73 + 18*x^72 + 18*x^71 + 104*x^70 + 74*x^69 + 60*x^68 + 85*x^67 + 72*x^66 + 117*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 82*x^7 + 104*x^6 + 10*x^5 + 60*x^4 + 125*x^3 + 72*x^2 + 93*x + 98, x^75 + 41*x^73 + 90*x^72 + 82*x^71 + 88*x^70 + 106*x^69 + 92*x^68 + 85*x^67 + 24*x^66 + 21*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 18*x^7 + 88*x^6 + 42*x^5 + 92*x^4 + 125*x^3 + 24*x^2 + 125*x + 58, x^75 + 41*x^73 + 30*x^72 + 114*x^71 + 88*x^70 + 42*x^69 + 100*x^68 + 117*x^67 + 120*x^66 + 21*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 50*x^7 + 88*x^6 + 106*x^5 + 100*x^4 + 29*x^3 + 120*x^2 + 125*x + 78, x^75 + 41*x^73 + 86*x^72 + 66*x^71 + 120*x^70 + 26*x^69 + 84*x^68 + 37*x^67 + 88*x^66 + 37*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 2*x^7 + 120*x^6 + 90*x^5 + 84*x^4 + 77*x^3 + 88*x^2 + 13*x + 38, x^75 + 41*x^73 + 122*x^72 + 66*x^71 + 40*x^70 + 26*x^69 + 108*x^68 + 37*x^67 + 8*x^66 + 37*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 2*x^7 + 40*x^6 + 90*x^5 + 108*x^4 + 77*x^3 + 8*x^2 + 13*x + 74, x^75 + 41*x^73 + 74*x^72 + 2*x^71 + 72*x^70 + 26*x^69 + 108*x^68 + 101*x^67 + 104*x^66 + 37*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 66*x^7 + 72*x^6 + 90*x^5 + 108*x^4 + 13*x^3 + 104*x^2 + 13*x + 122, x^75 + 41*x^73 + 102*x^72 + 98*x^71 + 120*x^70 + 58*x^69 + 116*x^68 + 5*x^67 + 88*x^66 + 5*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 34*x^7 + 120*x^6 + 122*x^5 + 116*x^4 + 45*x^3 + 88*x^2 + 109*x + 118, x^75 + 41*x^73 + 66*x^72 + 50*x^71 + 104*x^70 + 106*x^69 + 28*x^68 + 53*x^67 + 72*x^66 + 85*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 114*x^7 + 104*x^6 + 42*x^5 + 28*x^4 + 93*x^3 + 72*x^2 + 61*x + 82, x^75 + 41*x^73 + 98*x^72 + 82*x^71 + 72*x^70 + 74*x^69 + 124*x^68 + 21*x^67 + 104*x^66 + 117*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 18*x^7 + 72*x^6 + 10*x^5 + 124*x^4 + 61*x^3 + 104*x^2 + 93*x + 82, x^75 + 41*x^73 + 114*x^72 + 82*x^71 + 8*x^70 + 74*x^69 + 92*x^68 + 21*x^67 + 40*x^66 + 117*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 18*x^7 + 8*x^6 + 10*x^5 + 92*x^4 + 61*x^3 + 40*x^2 + 93*x + 98, x^75 + 41*x^73 + 34*x^72 + 34*x^71 + 120*x^70 + 90*x^69 + 44*x^68 + 5*x^67 + 120*x^66 + 37*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 98*x^7 + 120*x^6 + 26*x^5 + 44*x^4 + 45*x^3 + 120*x^2 + 13*x + 34, x^75 + 41*x^73 + 102*x^72 + 34*x^71 + 88*x^70 + 122*x^69 + 84*x^68 + 69*x^67 + 120*x^66 + 69*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 98*x^7 + 88*x^6 + 58*x^5 + 84*x^4 + 109*x^3 + 120*x^2 + 45*x + 22, x^75 + 41*x^73 + 50*x^72 + 2*x^71 + 120*x^70 + 122*x^69 + 12*x^68 + 37*x^67 + 120*x^66 + 5*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 66*x^7 + 120*x^6 + 58*x^5 + 12*x^4 + 77*x^3 + 120*x^2 + 109*x + 50, x^75 + 41*x^73 + 14*x^72 + 2*x^71 + 72*x^70 + 122*x^69 + 52*x^68 + 37*x^67 + 72*x^66 + 5*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 66*x^7 + 72*x^6 + 58*x^5 + 52*x^4 + 77*x^3 + 72*x^2 + 109*x + 78, x^75 + 41*x^73 + 22*x^72 + 18*x^71 + 104*x^70 + 106*x^69 + 4*x^68 + 21*x^67 + 40*x^66 + 21*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 82*x^7 + 104*x^6 + 42*x^5 + 4*x^4 + 61*x^3 + 40*x^2 + 125*x + 118, x^75 + 41*x^73 + 94*x^72 + 66*x^71 + 40*x^70 + 122*x^69 + 116*x^68 + 101*x^67 + 104*x^66 + 5*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 2*x^7 + 40*x^6 + 58*x^5 + 116*x^4 + 13*x^3 + 104*x^2 + 109*x + 62, x^75 + 41*x^73 + 30*x^72 + 50*x^71 + 24*x^70 + 106*x^69 + 36*x^68 + 53*x^67 + 56*x^66 + 85*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 114*x^7 + 24*x^6 + 42*x^5 + 36*x^4 + 93*x^3 + 56*x^2 + 61*x + 14, x^75 + 41*x^73 + 6*x^72 + 34*x^71 + 88*x^70 + 58*x^69 + 84*x^68 + 69*x^67 + 120*x^66 + 5*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 98*x^7 + 88*x^6 + 122*x^5 + 84*x^4 + 109*x^3 + 120*x^2 + 109*x + 118, x^75 + 41*x^73 + 22*x^72 + 50*x^71 + 8*x^70 + 10*x^69 + 36*x^68 + 117*x^67 + 8*x^66 + 117*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 114*x^7 + 8*x^6 + 74*x^5 + 36*x^4 + 29*x^3 + 8*x^2 + 93*x + 86, x^75 + 41*x^73 + 38*x^72 + 2*x^71 + 88*x^70 + 90*x^69 + 84*x^68 + 101*x^67 + 120*x^66 + 101*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 66*x^7 + 88*x^6 + 26*x^5 + 84*x^4 + 13*x^3 + 120*x^2 + 77*x + 86, x^75 + 41*x^73 + 106*x^72 + 114*x^71 + 56*x^70 + 10*x^69 + 92*x^68 + 53*x^67 + 56*x^66 + 117*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 50*x^7 + 56*x^6 + 74*x^5 + 92*x^4 + 93*x^3 + 56*x^2 + 93*x + 42, x^75 + 41*x^73 + 34*x^72 + 50*x^71 + 72*x^70 + 106*x^69 + 60*x^68 + 53*x^67 + 104*x^66 + 85*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 114*x^7 + 72*x^6 + 42*x^5 + 60*x^4 + 93*x^3 + 104*x^2 + 61*x + 82, x^75 + 41*x^73 + 110*x^72 + 50*x^71 + 56*x^70 + 42*x^69 + 36*x^68 + 53*x^67 + 24*x^66 + 21*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 114*x^7 + 56*x^6 + 106*x^5 + 36*x^4 + 93*x^3 + 24*x^2 + 125*x + 62, x^75 + 41*x^73 + 62*x^72 + 98*x^71 + 104*x^70 + 90*x^69 + 52*x^68 + 69*x^67 + 40*x^66 + 37*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 34*x^7 + 104*x^6 + 26*x^5 + 52*x^4 + 109*x^3 + 40*x^2 + 13*x + 30, x^75 + 41*x^73 + 110*x^72 + 50*x^71 + 120*x^70 + 106*x^69 + 36*x^68 + 53*x^67 + 88*x^66 + 85*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 114*x^7 + 120*x^6 + 42*x^5 + 36*x^4 + 93*x^3 + 88*x^2 + 61*x + 62, x^75 + 41*x^73 + 54*x^72 + 50*x^71 + 104*x^70 + 10*x^69 + 68*x^68 + 117*x^67 + 40*x^66 + 117*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 114*x^7 + 104*x^6 + 74*x^5 + 68*x^4 + 29*x^3 + 40*x^2 + 93*x + 22, x^75 + 41*x^73 + 98*x^72 + 66*x^71 + 56*x^70 + 122*x^69 + 108*x^68 + 101*x^67 + 56*x^66 + 5*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 2*x^7 + 56*x^6 + 58*x^5 + 108*x^4 + 13*x^3 + 56*x^2 + 109*x + 34, x^75 + 41*x^73 + 58*x^72 + 114*x^71 + 56*x^70 + 10*x^69 + 124*x^68 + 53*x^67 + 56*x^66 + 117*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 50*x^7 + 56*x^6 + 74*x^5 + 124*x^4 + 93*x^3 + 56*x^2 + 93*x + 58, x^75 + 41*x^73 + 34*x^72 + 34*x^71 + 56*x^70 + 26*x^69 + 44*x^68 + 5*x^67 + 56*x^66 + 101*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 98*x^7 + 56*x^6 + 90*x^5 + 44*x^4 + 45*x^3 + 56*x^2 + 77*x + 34, x^75 + 41*x^73 + 34*x^72 + 66*x^71 + 120*x^70 + 58*x^69 + 108*x^68 + 101*x^67 + 120*x^66 + 69*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 2*x^7 + 120*x^6 + 122*x^5 + 108*x^4 + 13*x^3 + 120*x^2 + 45*x + 98, x^75 + 41*x^73 + 34*x^72 + 18*x^71 + 8*x^70 + 10*x^69 + 60*x^68 + 85*x^67 + 40*x^66 + 53*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 82*x^7 + 8*x^6 + 74*x^5 + 60*x^4 + 125*x^3 + 40*x^2 + 29*x + 82, x^75 + 41*x^73 + 10*x^72 + 50*x^71 + 88*x^70 + 10*x^69 + 124*x^68 + 117*x^67 + 24*x^66 + 117*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 114*x^7 + 88*x^6 + 74*x^5 + 124*x^4 + 29*x^3 + 24*x^2 + 93*x + 106, x^75 + 41*x^73 + 58*x^72 + 34*x^71 + 8*x^70 + 58*x^69 + 12*x^68 + 69*x^67 + 40*x^66 + 5*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 98*x^7 + 8*x^6 + 122*x^5 + 12*x^4 + 109*x^3 + 40*x^2 + 109*x + 106, x^75 + 41*x^73 + 118*x^72 + 114*x^71 + 104*x^70 + 10*x^69 + 4*x^68 + 53*x^67 + 40*x^66 + 117*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 50*x^7 + 104*x^6 + 74*x^5 + 4*x^4 + 93*x^3 + 40*x^2 + 93*x + 22, x^75 + 41*x^73 + 110*x^72 + 34*x^71 + 40*x^70 + 26*x^69 + 84*x^68 + 5*x^67 + 104*x^66 + 101*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 98*x^7 + 40*x^6 + 90*x^5 + 84*x^4 + 45*x^3 + 104*x^2 + 77*x + 78, x^75 + 41*x^73 + 22*x^72 + 50*x^71 + 72*x^70 + 74*x^69 + 36*x^68 + 117*x^67 + 72*x^66 + 53*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 114*x^7 + 72*x^6 + 10*x^5 + 36*x^4 + 29*x^3 + 72*x^2 + 29*x + 86, x^75 + 41*x^73 + 74*x^72 + 114*x^71 + 24*x^70 + 74*x^69 + 60*x^68 + 53*x^67 + 88*x^66 + 53*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 50*x^7 + 24*x^6 + 10*x^5 + 60*x^4 + 93*x^3 + 88*x^2 + 29*x + 106, x^75 + 41*x^73 + 90*x^72 + 34*x^71 + 72*x^70 + 58*x^69 + 12*x^68 + 69*x^67 + 104*x^66 + 5*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 98*x^7 + 72*x^6 + 122*x^5 + 12*x^4 + 109*x^3 + 104*x^2 + 109*x + 74, x^75 + 41*x^73 + 106*x^72 + 18*x^71 + 88*x^70 + 106*x^69 + 60*x^68 + 21*x^67 + 24*x^66 + 21*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 82*x^7 + 88*x^6 + 42*x^5 + 60*x^4 + 61*x^3 + 24*x^2 + 125*x + 74, x^75 + 41*x^73 + 102*x^72 + 66*x^71 + 56*x^70 + 26*x^69 + 52*x^68 + 37*x^67 + 24*x^66 + 37*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 2*x^7 + 56*x^6 + 90*x^5 + 52*x^4 + 77*x^3 + 24*x^2 + 13*x + 54, x^75 + 41*x^73 + 18*x^72 + 114*x^71 + 8*x^70 + 42*x^69 + 92*x^68 + 117*x^67 + 40*x^66 + 21*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 50*x^7 + 8*x^6 + 106*x^5 + 92*x^4 + 29*x^3 + 40*x^2 + 125*x + 66, x^75 + 41*x^73 + 74*x^72 + 66*x^71 + 8*x^70 + 26*x^69 + 108*x^68 + 37*x^67 + 40*x^66 + 37*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 2*x^7 + 8*x^6 + 90*x^5 + 108*x^4 + 77*x^3 + 40*x^2 + 13*x + 122, x^75 + 41*x^73 + 62*x^72 + 66*x^71 + 40*x^70 + 122*x^69 + 52*x^68 + 101*x^67 + 104*x^66 + 5*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 2*x^7 + 40*x^6 + 58*x^5 + 52*x^4 + 13*x^3 + 104*x^2 + 109*x + 30, x^75 + 41*x^73 + 94*x^72 + 2*x^71 + 104*x^70 + 58*x^69 + 52*x^68 + 37*x^67 + 40*x^66 + 69*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 66*x^7 + 104*x^6 + 122*x^5 + 52*x^4 + 77*x^3 + 40*x^2 + 45*x + 126, x^75 + 41*x^73 + 126*x^72 + 2*x^71 + 8*x^70 + 122*x^69 + 84*x^68 + 37*x^67 + 8*x^66 + 5*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 66*x^7 + 8*x^6 + 58*x^5 + 84*x^4 + 77*x^3 + 8*x^2 + 109*x + 62, x^75 + 41*x^73 + 98*x^72 + 50*x^71 + 104*x^70 + 106*x^69 + 92*x^68 + 53*x^67 + 72*x^66 + 85*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 114*x^7 + 104*x^6 + 42*x^5 + 92*x^4 + 93*x^3 + 72*x^2 + 61*x + 114, x^75 + 41*x^73 + 98*x^72 + 18*x^71 + 72*x^70 + 10*x^69 + 124*x^68 + 85*x^67 + 104*x^66 + 53*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 82*x^7 + 72*x^6 + 74*x^5 + 124*x^4 + 125*x^3 + 104*x^2 + 29*x + 82, x^75 + 41*x^73 + 90*x^72 + 82*x^71 + 56*x^70 + 106*x^69 + 60*x^68 + 85*x^67 + 56*x^66 + 21*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 18*x^7 + 56*x^6 + 42*x^5 + 60*x^4 + 125*x^3 + 56*x^2 + 125*x + 90, x^75 + 41*x^73 + 58*x^72 + 114*x^71 + 88*x^70 + 74*x^69 + 92*x^68 + 53*x^67 + 24*x^66 + 53*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 50*x^7 + 88*x^6 + 10*x^5 + 92*x^4 + 93*x^3 + 24*x^2 + 29*x + 90, x^75 + 41*x^73 + 14*x^72 + 34*x^71 + 72*x^70 + 26*x^69 + 52*x^68 + 5*x^67 + 72*x^66 + 101*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 98*x^7 + 72*x^6 + 90*x^5 + 52*x^4 + 45*x^3 + 72*x^2 + 77*x + 78, x^75 + 41*x^73 + 86*x^72 + 66*x^71 + 88*x^70 + 90*x^69 + 116*x^68 + 37*x^67 + 120*x^66 + 101*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 2*x^7 + 88*x^6 + 26*x^5 + 116*x^4 + 77*x^3 + 120*x^2 + 77*x + 6, x^75 + 41*x^73 + 10*x^72 + 98*x^71 + 104*x^70 + 58*x^69 + 76*x^68 + 5*x^67 + 72*x^66 + 5*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 34*x^7 + 104*x^6 + 122*x^5 + 76*x^4 + 45*x^3 + 72*x^2 + 109*x + 90, x^75 + 41*x^73 + 86*x^72 + 98*x^71 + 88*x^70 + 58*x^69 + 52*x^68 + 5*x^67 + 120*x^66 + 5*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 34*x^7 + 88*x^6 + 122*x^5 + 52*x^4 + 45*x^3 + 120*x^2 + 109*x + 70, x^75 + 41*x^73 + 26*x^72 + 82*x^71 + 56*x^70 + 106*x^69 + 60*x^68 + 85*x^67 + 56*x^66 + 21*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 18*x^7 + 56*x^6 + 42*x^5 + 60*x^4 + 125*x^3 + 56*x^2 + 125*x + 26, x^75 + 41*x^73 + 114*x^72 + 18*x^71 + 40*x^70 + 10*x^69 + 124*x^68 + 85*x^67 + 8*x^66 + 53*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 82*x^7 + 40*x^6 + 74*x^5 + 124*x^4 + 125*x^3 + 8*x^2 + 29*x + 66, x^75 + 41*x^73 + 62*x^72 + 82*x^71 + 120*x^70 + 10*x^69 + 68*x^68 + 21*x^67 + 88*x^66 + 53*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 18*x^7 + 120*x^6 + 74*x^5 + 68*x^4 + 61*x^3 + 88*x^2 + 29*x + 78, x^75 + 41*x^73 + 2*x^72 + 66*x^71 + 120*x^70 + 122*x^69 + 108*x^68 + 101*x^67 + 120*x^66 + 5*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 2*x^7 + 120*x^6 + 58*x^5 + 108*x^4 + 13*x^3 + 120*x^2 + 109*x + 2, x^75 + 41*x^73 + 10*x^72 + 34*x^71 + 72*x^70 + 58*x^69 + 108*x^68 + 69*x^67 + 104*x^66 + 5*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 98*x^7 + 72*x^6 + 122*x^5 + 108*x^4 + 109*x^3 + 104*x^2 + 109*x + 58, x^75 + 41*x^73 + 14*x^72 + 114*x^71 + 24*x^70 + 106*x^69 + 68*x^68 + 117*x^67 + 56*x^66 + 85*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 50*x^7 + 24*x^6 + 42*x^5 + 68*x^4 + 29*x^3 + 56*x^2 + 61*x + 126, x^75 + 41*x^73 + 90*x^72 + 50*x^71 + 120*x^70 + 10*x^69 + 60*x^68 + 117*x^67 + 120*x^66 + 117*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 114*x^7 + 120*x^6 + 74*x^5 + 60*x^4 + 29*x^3 + 120*x^2 + 93*x + 90, x^75 + 41*x^73 + 98*x^72 + 66*x^71 + 88*x^70 + 122*x^69 + 12*x^68 + 101*x^67 + 24*x^66 + 5*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 2*x^7 + 88*x^6 + 58*x^5 + 12*x^4 + 13*x^3 + 24*x^2 + 109*x + 2, x^75 + 41*x^73 + 50*x^72 + 34*x^71 + 88*x^70 + 26*x^69 + 108*x^68 + 5*x^67 + 24*x^66 + 101*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 98*x^7 + 88*x^6 + 90*x^5 + 108*x^4 + 45*x^3 + 24*x^2 + 77*x + 82, x^75 + 41*x^73 + 78*x^72 + 98*x^71 + 40*x^70 + 90*x^69 + 20*x^68 + 69*x^67 + 104*x^66 + 37*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 34*x^7 + 40*x^6 + 26*x^5 + 20*x^4 + 109*x^3 + 104*x^2 + 13*x + 46, x^75 + 41*x^73 + 118*x^72 + 98*x^71 + 88*x^70 + 58*x^69 + 116*x^68 + 5*x^67 + 120*x^66 + 5*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 34*x^7 + 88*x^6 + 122*x^5 + 116*x^4 + 45*x^3 + 120*x^2 + 109*x + 102, x^75 + 41*x^73 + 58*x^72 + 98*x^71 + 40*x^70 + 58*x^69 + 108*x^68 + 5*x^67 + 8*x^66 + 5*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 34*x^7 + 40*x^6 + 122*x^5 + 108*x^4 + 45*x^3 + 8*x^2 + 109*x + 10, x^75 + 41*x^73 + 122*x^72 + 114*x^71 + 24*x^70 + 74*x^69 + 28*x^68 + 53*x^67 + 88*x^66 + 53*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 50*x^7 + 24*x^6 + 10*x^5 + 28*x^4 + 93*x^3 + 88*x^2 + 29*x + 90, x^75 + 41*x^73 + 98*x^72 + 82*x^71 + 40*x^70 + 74*x^69 + 92*x^68 + 21*x^67 + 8*x^66 + 117*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 18*x^7 + 40*x^6 + 10*x^5 + 92*x^4 + 61*x^3 + 8*x^2 + 93*x + 114, x^75 + 41*x^73 + 22*x^72 + 18*x^71 + 40*x^70 + 106*x^69 + 68*x^68 + 21*x^67 + 104*x^66 + 21*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 82*x^7 + 40*x^6 + 42*x^5 + 68*x^4 + 61*x^3 + 104*x^2 + 125*x + 54, x^75 + 41*x^73 + 10*x^72 + 34*x^71 + 40*x^70 + 122*x^69 + 12*x^68 + 69*x^67 + 8*x^66 + 69*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 98*x^7 + 40*x^6 + 58*x^5 + 12*x^4 + 109*x^3 + 8*x^2 + 45*x + 26, x^75 + 41*x^73 + 38*x^72 + 50*x^71 + 40*x^70 + 10*x^69 + 100*x^68 + 117*x^67 + 104*x^66 + 117*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 114*x^7 + 40*x^6 + 74*x^5 + 100*x^4 + 29*x^3 + 104*x^2 + 93*x + 6, x^75 + 41*x^73 + 98*x^72 + 50*x^71 + 104*x^70 + 42*x^69 + 28*x^68 + 53*x^67 + 72*x^66 + 21*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 114*x^7 + 104*x^6 + 106*x^5 + 28*x^4 + 93*x^3 + 72*x^2 + 125*x + 50, x^75 + 41*x^73 + 70*x^72 + 2*x^71 + 120*x^70 + 26*x^69 + 116*x^68 + 101*x^67 + 88*x^66 + 37*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 66*x^7 + 120*x^6 + 90*x^5 + 116*x^4 + 13*x^3 + 88*x^2 + 13*x + 22, x^75 + 41*x^73 + 6*x^72 + 18*x^71 + 72*x^70 + 42*x^69 + 4*x^68 + 21*x^67 + 72*x^66 + 85*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 82*x^7 + 72*x^6 + 106*x^5 + 4*x^4 + 61*x^3 + 72*x^2 + 61*x + 6, x^75 + 41*x^73 + 18*x^72 + 82*x^71 + 40*x^70 + 10*x^69 + 124*x^68 + 21*x^67 + 8*x^66 + 53*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 18*x^7 + 40*x^6 + 74*x^5 + 124*x^4 + 61*x^3 + 8*x^2 + 29*x + 34, x^75 + 41*x^73 + 126*x^72 + 34*x^71 + 8*x^70 + 90*x^69 + 20*x^68 + 5*x^67 + 8*x^66 + 37*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 98*x^7 + 8*x^6 + 26*x^5 + 20*x^4 + 45*x^3 + 8*x^2 + 13*x + 126, x^75 + 41*x^73 + 38*x^72 + 98*x^71 + 88*x^70 + 58*x^69 + 84*x^68 + 5*x^67 + 120*x^66 + 5*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 34*x^7 + 88*x^6 + 122*x^5 + 84*x^4 + 45*x^3 + 120*x^2 + 109*x + 86, x^75 + 41*x^73 + 2*x^72 + 82*x^71 + 8*x^70 + 74*x^69 + 124*x^68 + 21*x^67 + 40*x^66 + 117*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 18*x^7 + 8*x^6 + 10*x^5 + 124*x^4 + 61*x^3 + 40*x^2 + 93*x + 50, x^75 + 41*x^73 + 90*x^72 + 2*x^71 + 40*x^70 + 26*x^69 + 108*x^68 + 101*x^67 + 8*x^66 + 37*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 66*x^7 + 40*x^6 + 90*x^5 + 108*x^4 + 13*x^3 + 8*x^2 + 13*x + 106, x^75 + 41*x^73 + 58*x^72 + 2*x^71 + 40*x^70 + 90*x^69 + 108*x^68 + 101*x^67 + 8*x^66 + 101*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 66*x^7 + 40*x^6 + 26*x^5 + 108*x^4 + 13*x^3 + 8*x^2 + 77*x + 10, x^75 + 41*x^73 + 38*x^72 + 18*x^71 + 40*x^70 + 42*x^69 + 36*x^68 + 21*x^67 + 104*x^66 + 85*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 82*x^7 + 40*x^6 + 106*x^5 + 36*x^4 + 61*x^3 + 104*x^2 + 61*x + 70, x^75 + 41*x^73 + 74*x^72 + 50*x^71 + 120*x^70 + 74*x^69 + 92*x^68 + 117*x^67 + 120*x^66 + 53*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 114*x^7 + 120*x^6 + 10*x^5 + 92*x^4 + 29*x^3 + 120*x^2 + 29*x + 74, x^75 + 41*x^73 + 78*x^72 + 34*x^71 + 40*x^70 + 90*x^69 + 84*x^68 + 5*x^67 + 104*x^66 + 37*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 98*x^7 + 40*x^6 + 26*x^5 + 84*x^4 + 45*x^3 + 104*x^2 + 13*x + 110, x^75 + 41*x^73 + 98*x^72 + 98*x^71 + 120*x^70 + 26*x^69 + 44*x^68 + 69*x^67 + 120*x^66 + 101*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 34*x^7 + 120*x^6 + 90*x^5 + 44*x^4 + 109*x^3 + 120*x^2 + 77*x + 98, x^75 + 41*x^73 + 50*x^72 + 34*x^71 + 56*x^70 + 90*x^69 + 12*x^68 + 5*x^67 + 56*x^66 + 37*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 98*x^7 + 56*x^6 + 26*x^5 + 12*x^4 + 45*x^3 + 56*x^2 + 13*x + 50, x^75 + 41*x^73 + 30*x^72 + 82*x^71 + 56*x^70 + 74*x^69 + 4*x^68 + 21*x^67 + 24*x^66 + 117*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 18*x^7 + 56*x^6 + 10*x^5 + 4*x^4 + 61*x^3 + 24*x^2 + 93*x + 46, x^75 + 41*x^73 + 54*x^72 + 50*x^71 + 72*x^70 + 10*x^69 + 36*x^68 + 117*x^67 + 72*x^66 + 117*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 114*x^7 + 72*x^6 + 74*x^5 + 36*x^4 + 29*x^3 + 72*x^2 + 93*x + 54, x^75 + 41*x^73 + 82*x^72 + 98*x^71 + 24*x^70 + 90*x^69 + 108*x^68 + 69*x^67 + 88*x^66 + 37*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 34*x^7 + 24*x^6 + 26*x^5 + 108*x^4 + 109*x^3 + 88*x^2 + 13*x + 50, x^75 + 41*x^73 + 18*x^72 + 18*x^71 + 40*x^70 + 10*x^69 + 60*x^68 + 85*x^67 + 8*x^66 + 53*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 82*x^7 + 40*x^6 + 74*x^5 + 60*x^4 + 125*x^3 + 8*x^2 + 29*x + 98, x^75 + 41*x^73 + 102*x^72 + 34*x^71 + 120*x^70 + 122*x^69 + 116*x^68 + 69*x^67 + 88*x^66 + 69*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 98*x^7 + 120*x^6 + 58*x^5 + 116*x^4 + 109*x^3 + 88*x^2 + 45*x + 118, x^75 + 41*x^73 + 54*x^72 + 66*x^71 + 120*x^70 + 90*x^69 + 84*x^68 + 37*x^67 + 88*x^66 + 101*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 2*x^7 + 120*x^6 + 26*x^5 + 84*x^4 + 77*x^3 + 88*x^2 + 77*x + 70, x^75 + 41*x^73 + 98*x^72 + 34*x^71 + 88*x^70 + 26*x^69 + 76*x^68 + 5*x^67 + 24*x^66 + 101*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 98*x^7 + 88*x^6 + 90*x^5 + 76*x^4 + 45*x^3 + 24*x^2 + 77*x + 66, x^75 + 41*x^73 + 78*x^72 + 82*x^71 + 56*x^70 + 74*x^69 + 100*x^68 + 21*x^67 + 24*x^66 + 117*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 18*x^7 + 56*x^6 + 10*x^5 + 100*x^4 + 61*x^3 + 24*x^2 + 93*x + 30, x^75 + 41*x^73 + 98*x^72 + 82*x^71 + 8*x^70 + 10*x^69 + 124*x^68 + 21*x^67 + 40*x^66 + 53*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 18*x^7 + 8*x^6 + 74*x^5 + 124*x^4 + 61*x^3 + 40*x^2 + 29*x + 82, x^75 + 41*x^73 + 114*x^72 + 50*x^71 + 40*x^70 + 106*x^69 + 60*x^68 + 53*x^67 + 8*x^66 + 85*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 114*x^7 + 40*x^6 + 42*x^5 + 60*x^4 + 93*x^3 + 8*x^2 + 61*x + 2, x^75 + 41*x^73 + 42*x^72 + 66*x^71 + 104*x^70 + 90*x^69 + 76*x^68 + 37*x^67 + 72*x^66 + 101*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 2*x^7 + 104*x^6 + 26*x^5 + 76*x^4 + 77*x^3 + 72*x^2 + 77*x + 58, x^75 + 41*x^73 + 26*x^72 + 2*x^71 + 72*x^70 + 90*x^69 + 76*x^68 + 101*x^67 + 104*x^66 + 101*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 66*x^7 + 72*x^6 + 26*x^5 + 76*x^4 + 13*x^3 + 104*x^2 + 77*x + 74, x^75 + 41*x^73 + 42*x^72 + 114*x^71 + 24*x^70 + 10*x^69 + 60*x^68 + 53*x^67 + 88*x^66 + 117*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 50*x^7 + 24*x^6 + 74*x^5 + 60*x^4 + 93*x^3 + 88*x^2 + 93*x + 10, x^75 + 41*x^73 + 22*x^72 + 34*x^71 + 88*x^70 + 122*x^69 + 52*x^68 + 69*x^67 + 120*x^66 + 69*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 98*x^7 + 88*x^6 + 58*x^5 + 52*x^4 + 109*x^3 + 120*x^2 + 45*x + 6, x^75 + 41*x^73 + 66*x^72 + 82*x^71 + 104*x^70 + 10*x^69 + 28*x^68 + 21*x^67 + 72*x^66 + 53*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 18*x^7 + 104*x^6 + 74*x^5 + 28*x^4 + 61*x^3 + 72*x^2 + 29*x + 82, x^75 + 41*x^73 + 102*x^72 + 2*x^71 + 120*x^70 + 26*x^69 + 52*x^68 + 101*x^67 + 88*x^66 + 37*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 66*x^7 + 120*x^6 + 90*x^5 + 52*x^4 + 13*x^3 + 88*x^2 + 13*x + 54, x^75 + 41*x^73 + 66*x^72 + 50*x^71 + 40*x^70 + 42*x^69 + 28*x^68 + 53*x^67 + 8*x^66 + 21*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 114*x^7 + 40*x^6 + 106*x^5 + 28*x^4 + 93*x^3 + 8*x^2 + 125*x + 82, x^75 + 41*x^73 + 10*x^72 + 82*x^71 + 56*x^70 + 42*x^69 + 92*x^68 + 85*x^67 + 56*x^66 + 85*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 18*x^7 + 56*x^6 + 106*x^5 + 92*x^4 + 125*x^3 + 56*x^2 + 61*x + 10, x^75 + 41*x^73 + 10*x^72 + 50*x^71 + 120*x^70 + 74*x^69 + 92*x^68 + 117*x^67 + 120*x^66 + 53*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 114*x^7 + 120*x^6 + 10*x^5 + 92*x^4 + 29*x^3 + 120*x^2 + 29*x + 10, x^75 + 41*x^73 + 114*x^72 + 18*x^71 + 8*x^70 + 10*x^69 + 92*x^68 + 85*x^67 + 40*x^66 + 53*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 82*x^7 + 8*x^6 + 74*x^5 + 92*x^4 + 125*x^3 + 40*x^2 + 29*x + 98, x^75 + 41*x^73 + 114*x^72 + 114*x^71 + 40*x^70 + 106*x^69 + 124*x^68 + 117*x^67 + 8*x^66 + 85*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 50*x^7 + 40*x^6 + 42*x^5 + 124*x^4 + 29*x^3 + 8*x^2 + 61*x + 66, x^75 + 41*x^73 + 118*x^72 + 18*x^71 + 104*x^70 + 42*x^69 + 4*x^68 + 21*x^67 + 40*x^66 + 85*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 82*x^7 + 104*x^6 + 106*x^5 + 4*x^4 + 61*x^3 + 40*x^2 + 61*x + 22, x^75 + 41*x^73 + 94*x^72 + 114*x^71 + 24*x^70 + 106*x^69 + 100*x^68 + 117*x^67 + 56*x^66 + 85*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 50*x^7 + 24*x^6 + 42*x^5 + 100*x^4 + 29*x^3 + 56*x^2 + 61*x + 14, x^75 + 41*x^73 + 78*x^72 + 98*x^71 + 8*x^70 + 90*x^69 + 116*x^68 + 69*x^67 + 8*x^66 + 37*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 34*x^7 + 8*x^6 + 26*x^5 + 116*x^4 + 109*x^3 + 8*x^2 + 13*x + 78, x^75 + 41*x^73 + 118*x^72 + 50*x^71 + 72*x^70 + 10*x^69 + 36*x^68 + 117*x^67 + 72*x^66 + 117*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 114*x^7 + 72*x^6 + 74*x^5 + 36*x^4 + 29*x^3 + 72*x^2 + 93*x + 118, x^75 + 41*x^73 + 98*x^72 + 66*x^71 + 24*x^70 + 58*x^69 + 12*x^68 + 101*x^67 + 88*x^66 + 69*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 2*x^7 + 24*x^6 + 122*x^5 + 12*x^4 + 13*x^3 + 88*x^2 + 45*x + 2, x^75 + 41*x^73 + 14*x^72 + 34*x^71 + 72*x^70 + 90*x^69 + 116*x^68 + 5*x^67 + 72*x^66 + 37*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 98*x^7 + 72*x^6 + 26*x^5 + 116*x^4 + 45*x^3 + 72*x^2 + 13*x + 14, x^75 + 41*x^73 + 22*x^72 + 66*x^71 + 120*x^70 + 26*x^69 + 84*x^68 + 37*x^67 + 88*x^66 + 37*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 2*x^7 + 120*x^6 + 90*x^5 + 84*x^4 + 77*x^3 + 88*x^2 + 13*x + 102, x^75 + 41*x^73 + 34*x^72 + 50*x^71 + 8*x^70 + 42*x^69 + 60*x^68 + 53*x^67 + 40*x^66 + 21*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 114*x^7 + 8*x^6 + 106*x^5 + 60*x^4 + 93*x^3 + 40*x^2 + 125*x + 82, x^75 + 41*x^73 + 54*x^72 + 114*x^71 + 104*x^70 + 74*x^69 + 68*x^68 + 53*x^67 + 40*x^66 + 53*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 50*x^7 + 104*x^6 + 10*x^5 + 68*x^4 + 93*x^3 + 40*x^2 + 29*x + 22, x^75 + 41*x^73 + 26*x^72 + 66*x^71 + 40*x^70 + 26*x^69 + 44*x^68 + 37*x^67 + 8*x^66 + 37*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 2*x^7 + 40*x^6 + 90*x^5 + 44*x^4 + 77*x^3 + 8*x^2 + 13*x + 106, x^75 + 41*x^73 + 114*x^72 + 50*x^71 + 40*x^70 + 42*x^69 + 124*x^68 + 53*x^67 + 8*x^66 + 21*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 114*x^7 + 40*x^6 + 106*x^5 + 124*x^4 + 93*x^3 + 8*x^2 + 125*x + 66, x^75 + 41*x^73 + 14*x^72 + 82*x^71 + 88*x^70 + 10*x^69 + 68*x^68 + 21*x^67 + 120*x^66 + 53*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 18*x^7 + 88*x^6 + 74*x^5 + 68*x^4 + 61*x^3 + 120*x^2 + 29*x + 126, x^75 + 41*x^73 + 10*x^72 + 66*x^71 + 8*x^70 + 26*x^69 + 108*x^68 + 37*x^67 + 40*x^66 + 37*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 2*x^7 + 8*x^6 + 90*x^5 + 108*x^4 + 77*x^3 + 40*x^2 + 13*x + 58, x^75 + 41*x^73 + 18*x^72 + 98*x^71 + 56*x^70 + 26*x^69 + 76*x^68 + 69*x^67 + 56*x^66 + 101*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 34*x^7 + 56*x^6 + 90*x^5 + 76*x^4 + 109*x^3 + 56*x^2 + 77*x + 18, x^75 + 41*x^73 + 106*x^72 + 50*x^71 + 120*x^70 + 10*x^69 + 92*x^68 + 117*x^67 + 120*x^66 + 117*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 114*x^7 + 120*x^6 + 74*x^5 + 92*x^4 + 29*x^3 + 120*x^2 + 93*x + 42, x^75 + 41*x^73 + 106*x^72 + 50*x^71 + 88*x^70 + 74*x^69 + 124*x^68 + 117*x^67 + 24*x^66 + 53*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 114*x^7 + 88*x^6 + 10*x^5 + 124*x^4 + 29*x^3 + 24*x^2 + 29*x + 10, x^75 + 41*x^73 + 62*x^72 + 114*x^71 + 56*x^70 + 106*x^69 + 68*x^68 + 117*x^67 + 24*x^66 + 85*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 50*x^7 + 56*x^6 + 42*x^5 + 68*x^4 + 29*x^3 + 24*x^2 + 61*x + 78, x^75 + 41*x^73 + 30*x^72 + 98*x^71 + 104*x^70 + 26*x^69 + 52*x^68 + 69*x^67 + 40*x^66 + 101*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 34*x^7 + 104*x^6 + 90*x^5 + 52*x^4 + 109*x^3 + 40*x^2 + 77*x + 62, x^75 + 41*x^73 + 66*x^72 + 50*x^71 + 40*x^70 + 106*x^69 + 92*x^68 + 53*x^67 + 8*x^66 + 85*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 114*x^7 + 40*x^6 + 42*x^5 + 92*x^4 + 93*x^3 + 8*x^2 + 61*x + 18, x^75 + 41*x^73 + 42*x^72 + 66*x^71 + 8*x^70 + 90*x^69 + 108*x^68 + 37*x^67 + 40*x^66 + 101*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 2*x^7 + 8*x^6 + 26*x^5 + 108*x^4 + 77*x^3 + 40*x^2 + 77*x + 26, x^75 + 41*x^73 + 110*x^72 + 18*x^71 + 24*x^70 + 10*x^69 + 4*x^68 + 85*x^67 + 56*x^66 + 53*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 82*x^7 + 24*x^6 + 74*x^5 + 4*x^4 + 125*x^3 + 56*x^2 + 29*x + 94, x^75 + 41*x^73 + 78*x^72 + 98*x^71 + 8*x^70 + 26*x^69 + 52*x^68 + 69*x^67 + 8*x^66 + 101*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 34*x^7 + 8*x^6 + 90*x^5 + 52*x^4 + 109*x^3 + 8*x^2 + 77*x + 14, x^75 + 41*x^73 + 102*x^72 + 66*x^71 + 88*x^70 + 90*x^69 + 20*x^68 + 37*x^67 + 120*x^66 + 101*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 2*x^7 + 88*x^6 + 26*x^5 + 20*x^4 + 77*x^3 + 120*x^2 + 77*x + 86, x^75 + 41*x^73 + 22*x^72 + 114*x^71 + 104*x^70 + 10*x^69 + 68*x^68 + 53*x^67 + 40*x^66 + 117*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 50*x^7 + 104*x^6 + 74*x^5 + 68*x^4 + 93*x^3 + 40*x^2 + 93*x + 54, x^75 + 41*x^73 + 74*x^72 + 82*x^71 + 24*x^70 + 42*x^69 + 60*x^68 + 85*x^67 + 88*x^66 + 85*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 18*x^7 + 24*x^6 + 106*x^5 + 60*x^4 + 125*x^3 + 88*x^2 + 61*x + 106, x^75 + 41*x^73 + 126*x^72 + 66*x^71 + 72*x^70 + 58*x^69 + 20*x^68 + 101*x^67 + 72*x^66 + 69*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 2*x^7 + 72*x^6 + 122*x^5 + 20*x^4 + 13*x^3 + 72*x^2 + 45*x + 126, x^75 + 41*x^73 + 78*x^72 + 82*x^71 + 120*x^70 + 74*x^69 + 36*x^68 + 21*x^67 + 88*x^66 + 117*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 18*x^7 + 120*x^6 + 10*x^5 + 36*x^4 + 61*x^3 + 88*x^2 + 93*x + 94, x^75 + 41*x^73 + 78*x^72 + 82*x^71 + 88*x^70 + 74*x^69 + 4*x^68 + 21*x^67 + 120*x^66 + 117*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 18*x^7 + 88*x^6 + 10*x^5 + 4*x^4 + 61*x^3 + 120*x^2 + 93*x + 126, x^75 + 41*x^73 + 122*x^72 + 18*x^71 + 24*x^70 + 106*x^69 + 28*x^68 + 21*x^67 + 88*x^66 + 21*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 82*x^7 + 24*x^6 + 42*x^5 + 28*x^4 + 61*x^3 + 88*x^2 + 125*x + 90, x^75 + 41*x^73 + 82*x^72 + 18*x^71 + 8*x^70 + 10*x^69 + 28*x^68 + 85*x^67 + 40*x^66 + 53*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 82*x^7 + 8*x^6 + 74*x^5 + 28*x^4 + 125*x^3 + 40*x^2 + 29*x + 66, x^75 + 41*x^73 + 54*x^72 + 18*x^71 + 104*x^70 + 106*x^69 + 68*x^68 + 21*x^67 + 40*x^66 + 21*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 82*x^7 + 104*x^6 + 42*x^5 + 68*x^4 + 61*x^3 + 40*x^2 + 125*x + 22, x^75 + 41*x^73 + 70*x^72 + 82*x^71 + 40*x^70 + 106*x^69 + 100*x^68 + 85*x^67 + 104*x^66 + 21*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 18*x^7 + 40*x^6 + 42*x^5 + 100*x^4 + 125*x^3 + 104*x^2 + 125*x + 102, x^75 + 41*x^73 + 82*x^72 + 50*x^71 + 8*x^70 + 42*x^69 + 28*x^68 + 53*x^67 + 40*x^66 + 21*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 114*x^7 + 8*x^6 + 106*x^5 + 28*x^4 + 93*x^3 + 40*x^2 + 125*x + 66, x^75 + 41*x^73 + 30*x^72 + 114*x^71 + 56*x^70 + 42*x^69 + 68*x^68 + 117*x^67 + 24*x^66 + 21*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 50*x^7 + 56*x^6 + 106*x^5 + 68*x^4 + 29*x^3 + 24*x^2 + 125*x + 110, x^75 + 41*x^73 + 34*x^72 + 82*x^71 + 40*x^70 + 74*x^69 + 92*x^68 + 21*x^67 + 8*x^66 + 117*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 18*x^7 + 40*x^6 + 10*x^5 + 92*x^4 + 61*x^3 + 8*x^2 + 93*x + 50, x^75 + 41*x^73 + 54*x^72 + 2*x^71 + 120*x^70 + 90*x^69 + 20*x^68 + 101*x^67 + 88*x^66 + 101*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 66*x^7 + 120*x^6 + 26*x^5 + 20*x^4 + 13*x^3 + 88*x^2 + 77*x + 6, x^75 + 41*x^73 + 86*x^72 + 34*x^71 + 88*x^70 + 58*x^69 + 116*x^68 + 69*x^67 + 120*x^66 + 5*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 98*x^7 + 88*x^6 + 122*x^5 + 116*x^4 + 109*x^3 + 120*x^2 + 109*x + 6, x^75 + 41*x^73 + 6*x^72 + 50*x^71 + 40*x^70 + 74*x^69 + 100*x^68 + 117*x^67 + 104*x^66 + 53*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 114*x^7 + 40*x^6 + 10*x^5 + 100*x^4 + 29*x^3 + 104*x^2 + 29*x + 38, x^75 + 41*x^73 + 22*x^72 + 34*x^71 + 56*x^70 + 122*x^69 + 20*x^68 + 69*x^67 + 24*x^66 + 69*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 98*x^7 + 56*x^6 + 58*x^5 + 20*x^4 + 109*x^3 + 24*x^2 + 45*x + 38, x^75 + 41*x^73 + 106*x^72 + 114*x^71 + 120*x^70 + 10*x^69 + 28*x^68 + 53*x^67 + 120*x^66 + 117*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 50*x^7 + 120*x^6 + 74*x^5 + 28*x^4 + 93*x^3 + 120*x^2 + 93*x + 106, x^75 + 41*x^73 + 82*x^72 + 82*x^71 + 104*x^70 + 10*x^69 + 60*x^68 + 21*x^67 + 72*x^66 + 53*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 18*x^7 + 104*x^6 + 74*x^5 + 60*x^4 + 61*x^3 + 72*x^2 + 29*x + 34, x^75 + 41*x^73 + 106*x^72 + 18*x^71 + 24*x^70 + 106*x^69 + 124*x^68 + 21*x^67 + 88*x^66 + 21*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 82*x^7 + 24*x^6 + 42*x^5 + 124*x^4 + 61*x^3 + 88*x^2 + 125*x + 10, x^75 + 41*x^73 + 78*x^72 + 34*x^71 + 72*x^70 + 90*x^69 + 116*x^68 + 5*x^67 + 72*x^66 + 37*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 98*x^7 + 72*x^6 + 26*x^5 + 116*x^4 + 45*x^3 + 72*x^2 + 13*x + 78, x^75 + 41*x^73 + 22*x^72 + 50*x^71 + 104*x^70 + 74*x^69 + 68*x^68 + 117*x^67 + 40*x^66 + 53*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 114*x^7 + 104*x^6 + 10*x^5 + 68*x^4 + 29*x^3 + 40*x^2 + 29*x + 54, x^75 + 41*x^73 + 114*x^72 + 82*x^71 + 104*x^70 + 74*x^69 + 60*x^68 + 21*x^67 + 72*x^66 + 117*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 18*x^7 + 104*x^6 + 10*x^5 + 60*x^4 + 61*x^3 + 72*x^2 + 93*x + 2, x^75 + 41*x^73 + 106*x^72 + 34*x^71 + 72*x^70 + 58*x^69 + 44*x^68 + 69*x^67 + 104*x^66 + 5*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 98*x^7 + 72*x^6 + 122*x^5 + 44*x^4 + 109*x^3 + 104*x^2 + 109*x + 26, x^75 + 41*x^73 + 14*x^72 + 66*x^71 + 8*x^70 + 122*x^69 + 52*x^68 + 101*x^67 + 8*x^66 + 5*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 2*x^7 + 8*x^6 + 58*x^5 + 52*x^4 + 13*x^3 + 8*x^2 + 109*x + 78, x^75 + 41*x^73 + 6*x^72 + 98*x^71 + 56*x^70 + 122*x^69 + 52*x^68 + 5*x^67 + 24*x^66 + 69*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 34*x^7 + 56*x^6 + 58*x^5 + 52*x^4 + 45*x^3 + 24*x^2 + 45*x + 22, x^75 + 41*x^73 + 34*x^72 + 2*x^71 + 56*x^70 + 58*x^69 + 108*x^68 + 37*x^67 + 56*x^66 + 69*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 66*x^7 + 56*x^6 + 122*x^5 + 108*x^4 + 77*x^3 + 56*x^2 + 45*x + 98, x^75 + 41*x^73 + 106*x^72 + 66*x^71 + 40*x^70 + 90*x^69 + 12*x^68 + 37*x^67 + 8*x^66 + 101*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 2*x^7 + 40*x^6 + 26*x^5 + 12*x^4 + 77*x^3 + 8*x^2 + 77*x + 58, x^75 + 41*x^73 + 74*x^72 + 98*x^71 + 72*x^70 + 122*x^69 + 108*x^68 + 5*x^67 + 104*x^66 + 69*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 34*x^7 + 72*x^6 + 58*x^5 + 108*x^4 + 45*x^3 + 104*x^2 + 45*x + 122, x^75 + 41*x^73 + 106*x^72 + 18*x^71 + 120*x^70 + 42*x^69 + 28*x^68 + 21*x^67 + 120*x^66 + 85*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 82*x^7 + 120*x^6 + 106*x^5 + 28*x^4 + 61*x^3 + 120*x^2 + 61*x + 106, x^75 + 41*x^73 + 82*x^72 + 18*x^71 + 8*x^70 + 74*x^69 + 92*x^68 + 85*x^67 + 40*x^66 + 117*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 82*x^7 + 8*x^6 + 10*x^5 + 92*x^4 + 125*x^3 + 40*x^2 + 93*x + 2, x^75 + 41*x^73 + 2*x^72 + 114*x^71 + 104*x^70 + 42*x^69 + 28*x^68 + 117*x^67 + 72*x^66 + 21*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 50*x^7 + 104*x^6 + 106*x^5 + 28*x^4 + 29*x^3 + 72*x^2 + 125*x + 18, x^75 + 41*x^73 + 2*x^72 + 98*x^71 + 88*x^70 + 90*x^69 + 12*x^68 + 69*x^67 + 24*x^66 + 37*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 34*x^7 + 88*x^6 + 26*x^5 + 12*x^4 + 109*x^3 + 24*x^2 + 13*x + 98, x^75 + 41*x^73 + 50*x^72 + 50*x^71 + 72*x^70 + 106*x^69 + 92*x^68 + 53*x^67 + 104*x^66 + 85*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 114*x^7 + 72*x^6 + 42*x^5 + 92*x^4 + 93*x^3 + 104*x^2 + 61*x + 34, x^75 + 41*x^73 + 38*x^72 + 66*x^71 + 88*x^70 + 90*x^69 + 20*x^68 + 37*x^67 + 120*x^66 + 101*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 2*x^7 + 88*x^6 + 26*x^5 + 20*x^4 + 77*x^3 + 120*x^2 + 77*x + 22, x^75 + 41*x^73 + 102*x^72 + 2*x^71 + 120*x^70 + 90*x^69 + 116*x^68 + 101*x^67 + 88*x^66 + 101*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 66*x^7 + 120*x^6 + 26*x^5 + 116*x^4 + 13*x^3 + 88*x^2 + 77*x + 118, x^75 + 41*x^73 + 46*x^72 + 2*x^71 + 8*x^70 + 122*x^69 + 52*x^68 + 37*x^67 + 8*x^66 + 5*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 66*x^7 + 8*x^6 + 58*x^5 + 52*x^4 + 77*x^3 + 8*x^2 + 109*x + 46, x^75 + 41*x^73 + 22*x^72 + 18*x^71 + 104*x^70 + 42*x^69 + 68*x^68 + 21*x^67 + 40*x^66 + 85*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 82*x^7 + 104*x^6 + 106*x^5 + 68*x^4 + 61*x^3 + 40*x^2 + 61*x + 54, x^75 + 41*x^73 + 26*x^72 + 2*x^71 + 40*x^70 + 26*x^69 + 108*x^68 + 101*x^67 + 8*x^66 + 37*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 66*x^7 + 40*x^6 + 90*x^5 + 108*x^4 + 13*x^3 + 8*x^2 + 13*x + 42, x^75 + 41*x^73 + 22*x^72 + 2*x^71 + 120*x^70 + 90*x^69 + 84*x^68 + 101*x^67 + 88*x^66 + 101*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 66*x^7 + 120*x^6 + 26*x^5 + 84*x^4 + 13*x^3 + 88*x^2 + 77*x + 102, x^75 + 41*x^73 + 34*x^72 + 82*x^71 + 72*x^70 + 10*x^69 + 60*x^68 + 21*x^67 + 104*x^66 + 53*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 18*x^7 + 72*x^6 + 74*x^5 + 60*x^4 + 61*x^3 + 104*x^2 + 29*x + 82, x^75 + 41*x^73 + 46*x^72 + 66*x^71 + 40*x^70 + 58*x^69 + 84*x^68 + 101*x^67 + 104*x^66 + 69*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 2*x^7 + 40*x^6 + 122*x^5 + 84*x^4 + 13*x^3 + 104*x^2 + 45*x + 14, x^75 + 41*x^73 + 74*x^72 + 98*x^71 + 104*x^70 + 58*x^69 + 76*x^68 + 5*x^67 + 72*x^66 + 5*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 34*x^7 + 104*x^6 + 122*x^5 + 76*x^4 + 45*x^3 + 72*x^2 + 109*x + 26, x^75 + 41*x^73 + 94*x^72 + 98*x^71 + 104*x^70 + 90*x^69 + 116*x^68 + 69*x^67 + 40*x^66 + 37*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 34*x^7 + 104*x^6 + 26*x^5 + 116*x^4 + 109*x^3 + 40*x^2 + 13*x + 62, x^75 + 41*x^73 + 90*x^72 + 50*x^71 + 88*x^70 + 74*x^69 + 92*x^68 + 117*x^67 + 24*x^66 + 53*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 114*x^7 + 88*x^6 + 10*x^5 + 92*x^4 + 29*x^3 + 24*x^2 + 29*x + 58, x^75 + 41*x^73 + 122*x^72 + 66*x^71 + 8*x^70 + 90*x^69 + 12*x^68 + 37*x^67 + 40*x^66 + 101*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 2*x^7 + 8*x^6 + 26*x^5 + 12*x^4 + 77*x^3 + 40*x^2 + 77*x + 42, x^75 + 41*x^73 + 90*x^72 + 18*x^71 + 56*x^70 + 42*x^69 + 60*x^68 + 21*x^67 + 56*x^66 + 85*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 82*x^7 + 56*x^6 + 106*x^5 + 60*x^4 + 61*x^3 + 56*x^2 + 61*x + 90, x^75 + 41*x^73 + 94*x^72 + 18*x^71 + 56*x^70 + 74*x^69 + 68*x^68 + 85*x^67 + 24*x^66 + 117*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 82*x^7 + 56*x^6 + 10*x^5 + 68*x^4 + 125*x^3 + 24*x^2 + 93*x + 46, x^75 + 41*x^73 + 106*x^72 + 66*x^71 + 72*x^70 + 90*x^69 + 44*x^68 + 37*x^67 + 104*x^66 + 101*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 2*x^7 + 72*x^6 + 26*x^5 + 44*x^4 + 77*x^3 + 104*x^2 + 77*x + 26, x^75 + 41*x^73 + 110*x^72 + 66*x^71 + 104*x^70 + 122*x^69 + 84*x^68 + 101*x^67 + 40*x^66 + 5*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 2*x^7 + 104*x^6 + 58*x^5 + 84*x^4 + 13*x^3 + 40*x^2 + 109*x + 78, x^75 + 41*x^73 + 30*x^72 + 18*x^71 + 24*x^70 + 10*x^69 + 100*x^68 + 85*x^67 + 56*x^66 + 53*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 82*x^7 + 24*x^6 + 74*x^5 + 100*x^4 + 125*x^3 + 56*x^2 + 29*x + 78, x^75 + 41*x^73 + 70*x^72 + 98*x^71 + 88*x^70 + 122*x^69 + 84*x^68 + 5*x^67 + 120*x^66 + 69*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 34*x^7 + 88*x^6 + 58*x^5 + 84*x^4 + 45*x^3 + 120*x^2 + 45*x + 54, x^75 + 41*x^73 + 10*x^72 + 114*x^71 + 88*x^70 + 74*x^69 + 124*x^68 + 53*x^67 + 24*x^66 + 53*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 50*x^7 + 88*x^6 + 10*x^5 + 124*x^4 + 93*x^3 + 24*x^2 + 29*x + 106, x^75 + 41*x^73 + 70*x^72 + 98*x^71 + 88*x^70 + 58*x^69 + 20*x^68 + 5*x^67 + 120*x^66 + 5*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 34*x^7 + 88*x^6 + 122*x^5 + 20*x^4 + 45*x^3 + 120*x^2 + 109*x + 118, x^75 + 41*x^73 + 62*x^72 + 66*x^71 + 72*x^70 + 122*x^69 + 84*x^68 + 101*x^67 + 72*x^66 + 5*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 2*x^7 + 72*x^6 + 58*x^5 + 84*x^4 + 13*x^3 + 72*x^2 + 109*x + 126, x^75 + 41*x^73 + 126*x^72 + 66*x^71 + 104*x^70 + 58*x^69 + 52*x^68 + 101*x^67 + 40*x^66 + 69*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 2*x^7 + 104*x^6 + 122*x^5 + 52*x^4 + 13*x^3 + 40*x^2 + 45*x + 94, x^75 + 41*x^73 + 18*x^72 + 34*x^71 + 24*x^70 + 26*x^69 + 108*x^68 + 5*x^67 + 88*x^66 + 101*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 98*x^7 + 24*x^6 + 90*x^5 + 108*x^4 + 45*x^3 + 88*x^2 + 77*x + 114, x^75 + 41*x^73 + 50*x^72 + 82*x^71 + 40*x^70 + 10*x^69 + 60*x^68 + 21*x^67 + 8*x^66 + 53*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 18*x^7 + 40*x^6 + 74*x^5 + 60*x^4 + 61*x^3 + 8*x^2 + 29*x + 66, x^75 + 41*x^73 + 6*x^72 + 2*x^71 + 120*x^70 + 26*x^69 + 116*x^68 + 101*x^67 + 88*x^66 + 37*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 66*x^7 + 120*x^6 + 90*x^5 + 116*x^4 + 13*x^3 + 88*x^2 + 13*x + 86, x^75 + 41*x^73 + 46*x^72 + 98*x^71 + 8*x^70 + 90*x^69 + 52*x^68 + 69*x^67 + 8*x^66 + 37*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 34*x^7 + 8*x^6 + 26*x^5 + 52*x^4 + 109*x^3 + 8*x^2 + 13*x + 46, x^75 + 41*x^73 + 90*x^72 + 114*x^71 + 56*x^70 + 74*x^69 + 124*x^68 + 53*x^67 + 56*x^66 + 53*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 50*x^7 + 56*x^6 + 10*x^5 + 124*x^4 + 93*x^3 + 56*x^2 + 29*x + 26, x^75 + 41*x^73 + 126*x^72 + 50*x^71 + 120*x^70 + 42*x^69 + 4*x^68 + 53*x^67 + 88*x^66 + 21*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 114*x^7 + 120*x^6 + 106*x^5 + 4*x^4 + 93*x^3 + 88*x^2 + 125*x + 78, x^75 + 41*x^73 + 94*x^72 + 18*x^71 + 120*x^70 + 10*x^69 + 68*x^68 + 85*x^67 + 88*x^66 + 53*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 82*x^7 + 120*x^6 + 74*x^5 + 68*x^4 + 125*x^3 + 88*x^2 + 29*x + 46, x^75 + 41*x^73 + 22*x^72 + 34*x^71 + 120*x^70 + 122*x^69 + 84*x^68 + 69*x^67 + 88*x^66 + 69*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 98*x^7 + 120*x^6 + 58*x^5 + 84*x^4 + 109*x^3 + 88*x^2 + 45*x + 102, x^75 + 41*x^73 + 26*x^72 + 2*x^71 + 8*x^70 + 26*x^69 + 76*x^68 + 101*x^67 + 40*x^66 + 37*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 66*x^7 + 8*x^6 + 90*x^5 + 76*x^4 + 13*x^3 + 40*x^2 + 13*x + 74, x^75 + 41*x^73 + 6*x^72 + 66*x^71 + 88*x^70 + 90*x^69 + 84*x^68 + 37*x^67 + 120*x^66 + 101*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 2*x^7 + 88*x^6 + 26*x^5 + 84*x^4 + 77*x^3 + 120*x^2 + 77*x + 118, x^75 + 41*x^73 + 62*x^72 + 98*x^71 + 72*x^70 + 26*x^69 + 84*x^68 + 69*x^67 + 72*x^66 + 101*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 34*x^7 + 72*x^6 + 90*x^5 + 84*x^4 + 109*x^3 + 72*x^2 + 77*x + 126, x^75 + 41*x^73 + 126*x^72 + 50*x^71 + 56*x^70 + 42*x^69 + 68*x^68 + 53*x^67 + 24*x^66 + 21*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 114*x^7 + 56*x^6 + 106*x^5 + 68*x^4 + 93*x^3 + 24*x^2 + 125*x + 14, x^75 + 41*x^73 + 82*x^72 + 98*x^71 + 24*x^70 + 26*x^69 + 44*x^68 + 69*x^67 + 88*x^66 + 101*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 34*x^7 + 24*x^6 + 90*x^5 + 44*x^4 + 109*x^3 + 88*x^2 + 77*x + 114, x^75 + 41*x^73 + 90*x^72 + 18*x^71 + 120*x^70 + 106*x^69 + 60*x^68 + 21*x^67 + 120*x^66 + 21*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 82*x^7 + 120*x^6 + 42*x^5 + 60*x^4 + 61*x^3 + 120*x^2 + 125*x + 90, x^75 + 41*x^73 + 78*x^72 + 2*x^71 + 104*x^70 + 58*x^69 + 20*x^68 + 37*x^67 + 40*x^66 + 69*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 66*x^7 + 104*x^6 + 122*x^5 + 20*x^4 + 77*x^3 + 40*x^2 + 45*x + 46, x^75 + 41*x^73 + 66*x^72 + 18*x^71 + 72*x^70 + 10*x^69 + 60*x^68 + 85*x^67 + 104*x^66 + 53*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 82*x^7 + 72*x^6 + 74*x^5 + 60*x^4 + 125*x^3 + 104*x^2 + 29*x + 50, x^75 + 41*x^73 + 26*x^72 + 50*x^71 + 56*x^70 + 10*x^69 + 124*x^68 + 117*x^67 + 56*x^66 + 117*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 114*x^7 + 56*x^6 + 74*x^5 + 124*x^4 + 29*x^3 + 56*x^2 + 93*x + 90, x^75 + 41*x^73 + 102*x^72 + 34*x^71 + 56*x^70 + 58*x^69 + 116*x^68 + 69*x^67 + 24*x^66 + 5*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 98*x^7 + 56*x^6 + 122*x^5 + 116*x^4 + 109*x^3 + 24*x^2 + 109*x + 118, x^75 + 41*x^73 + 26*x^72 + 34*x^71 + 104*x^70 + 122*x^69 + 108*x^68 + 69*x^67 + 72*x^66 + 69*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 98*x^7 + 104*x^6 + 58*x^5 + 108*x^4 + 109*x^3 + 72*x^2 + 45*x + 42, x^75 + 41*x^73 + 6*x^72 + 34*x^71 + 56*x^70 + 58*x^69 + 52*x^68 + 69*x^67 + 24*x^66 + 5*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 98*x^7 + 56*x^6 + 122*x^5 + 52*x^4 + 109*x^3 + 24*x^2 + 109*x + 22, x^75 + 41*x^73 + 70*x^72 + 82*x^71 + 8*x^70 + 42*x^69 + 4*x^68 + 85*x^67 + 8*x^66 + 85*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 18*x^7 + 8*x^6 + 106*x^5 + 4*x^4 + 125*x^3 + 8*x^2 + 61*x + 70, x^75 + 41*x^73 + 66*x^72 + 66*x^71 + 120*x^70 + 58*x^69 + 44*x^68 + 101*x^67 + 120*x^66 + 69*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 2*x^7 + 120*x^6 + 122*x^5 + 44*x^4 + 13*x^3 + 120*x^2 + 45*x + 2, x^75 + 41*x^73 + 30*x^72 + 114*x^71 + 24*x^70 + 106*x^69 + 100*x^68 + 117*x^67 + 56*x^66 + 85*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 50*x^7 + 24*x^6 + 42*x^5 + 100*x^4 + 29*x^3 + 56*x^2 + 61*x + 78, x^75 + 41*x^73 + 58*x^72 + 18*x^71 + 120*x^70 + 106*x^69 + 124*x^68 + 21*x^67 + 120*x^66 + 21*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 82*x^7 + 120*x^6 + 42*x^5 + 124*x^4 + 61*x^3 + 120*x^2 + 125*x + 58, x^75 + 41*x^73 + 18*x^72 + 18*x^71 + 8*x^70 + 74*x^69 + 92*x^68 + 85*x^67 + 40*x^66 + 117*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 82*x^7 + 8*x^6 + 10*x^5 + 92*x^4 + 125*x^3 + 40*x^2 + 93*x + 66, x^75 + 41*x^73 + 106*x^72 + 2*x^71 + 8*x^70 + 90*x^69 + 44*x^68 + 101*x^67 + 40*x^66 + 101*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 66*x^7 + 8*x^6 + 26*x^5 + 44*x^4 + 13*x^3 + 40*x^2 + 77*x + 26, x^75 + 41*x^73 + 78*x^72 + 18*x^71 + 88*x^70 + 10*x^69 + 4*x^68 + 85*x^67 + 120*x^66 + 53*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 82*x^7 + 88*x^6 + 74*x^5 + 4*x^4 + 125*x^3 + 120*x^2 + 29*x + 126, x^75 + 41*x^73 + 118*x^72 + 50*x^71 + 104*x^70 + 74*x^69 + 4*x^68 + 117*x^67 + 40*x^66 + 53*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 114*x^7 + 104*x^6 + 10*x^5 + 4*x^4 + 29*x^3 + 40*x^2 + 29*x + 22, x^75 + 41*x^73 + 62*x^72 + 50*x^71 + 88*x^70 + 42*x^69 + 100*x^68 + 53*x^67 + 120*x^66 + 21*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 114*x^7 + 88*x^6 + 106*x^5 + 100*x^4 + 93*x^3 + 120*x^2 + 125*x + 46, x^75 + 41*x^73 + 54*x^72 + 50*x^71 + 40*x^70 + 10*x^69 + 4*x^68 + 117*x^67 + 104*x^66 + 117*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 114*x^7 + 40*x^6 + 74*x^5 + 4*x^4 + 29*x^3 + 104*x^2 + 93*x + 86, x^75 + 41*x^73 + 22*x^72 + 34*x^71 + 24*x^70 + 122*x^69 + 116*x^68 + 69*x^67 + 56*x^66 + 69*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 98*x^7 + 24*x^6 + 58*x^5 + 116*x^4 + 109*x^3 + 56*x^2 + 45*x + 70, x^75 + 41*x^73 + 118*x^72 + 34*x^71 + 24*x^70 + 58*x^69 + 116*x^68 + 69*x^67 + 56*x^66 + 5*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 98*x^7 + 24*x^6 + 122*x^5 + 116*x^4 + 109*x^3 + 56*x^2 + 109*x + 102, x^75 + 41*x^73 + 62*x^72 + 98*x^71 + 40*x^70 + 90*x^69 + 116*x^68 + 69*x^67 + 104*x^66 + 37*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 34*x^7 + 40*x^6 + 26*x^5 + 116*x^4 + 109*x^3 + 104*x^2 + 13*x + 94, x^75 + 41*x^73 + 94*x^72 + 66*x^71 + 40*x^70 + 58*x^69 + 52*x^68 + 101*x^67 + 104*x^66 + 69*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 2*x^7 + 40*x^6 + 122*x^5 + 52*x^4 + 13*x^3 + 104*x^2 + 45*x + 126, x^75 + 41*x^73 + 126*x^72 + 98*x^71 + 40*x^70 + 26*x^69 + 52*x^68 + 69*x^67 + 104*x^66 + 101*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 34*x^7 + 40*x^6 + 90*x^5 + 52*x^4 + 109*x^3 + 104*x^2 + 77*x + 94, x^75 + 41*x^73 + 42*x^72 + 2*x^71 + 104*x^70 + 90*x^69 + 12*x^68 + 101*x^67 + 72*x^66 + 101*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 66*x^7 + 104*x^6 + 26*x^5 + 12*x^4 + 13*x^3 + 72*x^2 + 77*x + 122, x^75 + 41*x^73 + 114*x^72 + 50*x^71 + 72*x^70 + 42*x^69 + 28*x^68 + 53*x^67 + 104*x^66 + 21*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 114*x^7 + 72*x^6 + 106*x^5 + 28*x^4 + 93*x^3 + 104*x^2 + 125*x + 34, x^75 + 41*x^73 + 30*x^72 + 114*x^71 + 120*x^70 + 106*x^69 + 68*x^68 + 117*x^67 + 88*x^66 + 85*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 50*x^7 + 120*x^6 + 42*x^5 + 68*x^4 + 29*x^3 + 88*x^2 + 61*x + 110, x^75 + 41*x^73 + 90*x^72 + 114*x^71 + 56*x^70 + 10*x^69 + 60*x^68 + 53*x^67 + 56*x^66 + 117*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 50*x^7 + 56*x^6 + 74*x^5 + 60*x^4 + 93*x^3 + 56*x^2 + 93*x + 90, x^75 + 41*x^73 + 2*x^72 + 2*x^71 + 24*x^70 + 122*x^69 + 76*x^68 + 37*x^67 + 88*x^66 + 5*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 66*x^7 + 24*x^6 + 58*x^5 + 76*x^4 + 77*x^3 + 88*x^2 + 109*x + 34, x^75 + 41*x^73 + 6*x^72 + 66*x^71 + 120*x^70 + 90*x^69 + 116*x^68 + 37*x^67 + 88*x^66 + 101*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 2*x^7 + 120*x^6 + 26*x^5 + 116*x^4 + 77*x^3 + 88*x^2 + 77*x + 86, x^75 + 41*x^73 + 94*x^72 + 50*x^71 + 24*x^70 + 106*x^69 + 36*x^68 + 53*x^67 + 56*x^66 + 85*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 114*x^7 + 24*x^6 + 42*x^5 + 36*x^4 + 93*x^3 + 56*x^2 + 61*x + 78, x^75 + 41*x^73 + 46*x^72 + 34*x^71 + 40*x^70 + 26*x^69 + 84*x^68 + 5*x^67 + 104*x^66 + 101*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 98*x^7 + 40*x^6 + 90*x^5 + 84*x^4 + 45*x^3 + 104*x^2 + 77*x + 14, x^75 + 41*x^73 + 46*x^72 + 98*x^71 + 8*x^70 + 26*x^69 + 116*x^68 + 69*x^67 + 8*x^66 + 101*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 34*x^7 + 8*x^6 + 90*x^5 + 116*x^4 + 109*x^3 + 8*x^2 + 77*x + 110, x^75 + 41*x^73 + 22*x^72 + 82*x^71 + 40*x^70 + 106*x^69 + 4*x^68 + 85*x^67 + 104*x^66 + 21*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 18*x^7 + 40*x^6 + 42*x^5 + 4*x^4 + 125*x^3 + 104*x^2 + 125*x + 118, x^75 + 41*x^73 + 70*x^72 + 82*x^71 + 72*x^70 + 42*x^69 + 68*x^68 + 85*x^67 + 72*x^66 + 85*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 18*x^7 + 72*x^6 + 106*x^5 + 68*x^4 + 125*x^3 + 72*x^2 + 61*x + 6, x^75 + 41*x^73 + 110*x^72 + 114*x^71 + 24*x^70 + 42*x^69 + 68*x^68 + 117*x^67 + 56*x^66 + 21*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 50*x^7 + 24*x^6 + 106*x^5 + 68*x^4 + 29*x^3 + 56*x^2 + 125*x + 30, x^75 + 41*x^73 + 86*x^72 + 50*x^71 + 72*x^70 + 10*x^69 + 100*x^68 + 117*x^67 + 72*x^66 + 117*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 114*x^7 + 72*x^6 + 74*x^5 + 100*x^4 + 29*x^3 + 72*x^2 + 93*x + 86, x^75 + 41*x^73 + 114*x^72 + 18*x^71 + 104*x^70 + 10*x^69 + 60*x^68 + 85*x^67 + 72*x^66 + 53*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 82*x^7 + 104*x^6 + 74*x^5 + 60*x^4 + 125*x^3 + 72*x^2 + 29*x + 2, x^75 + 41*x^73 + 54*x^72 + 82*x^71 + 104*x^70 + 106*x^69 + 4*x^68 + 85*x^67 + 40*x^66 + 21*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 18*x^7 + 104*x^6 + 42*x^5 + 4*x^4 + 125*x^3 + 40*x^2 + 125*x + 86, x^75 + 41*x^73 + 82*x^72 + 18*x^71 + 72*x^70 + 10*x^69 + 92*x^68 + 85*x^67 + 104*x^66 + 53*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 82*x^7 + 72*x^6 + 74*x^5 + 92*x^4 + 125*x^3 + 104*x^2 + 29*x + 2, x^75 + 41*x^73 + 78*x^72 + 66*x^71 + 104*x^70 + 58*x^69 + 84*x^68 + 101*x^67 + 40*x^66 + 69*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 2*x^7 + 104*x^6 + 122*x^5 + 84*x^4 + 13*x^3 + 40*x^2 + 45*x + 110, x^75 + 41*x^73 + 102*x^72 + 34*x^71 + 88*x^70 + 58*x^69 + 20*x^68 + 69*x^67 + 120*x^66 + 5*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 98*x^7 + 88*x^6 + 122*x^5 + 20*x^4 + 109*x^3 + 120*x^2 + 109*x + 86, x^75 + 41*x^73 + 98*x^72 + 66*x^71 + 24*x^70 + 122*x^69 + 76*x^68 + 101*x^67 + 88*x^66 + 5*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 2*x^7 + 24*x^6 + 58*x^5 + 76*x^4 + 13*x^3 + 88*x^2 + 109*x + 66, x^75 + 41*x^73 + 90*x^72 + 98*x^71 + 72*x^70 + 58*x^69 + 76*x^68 + 5*x^67 + 104*x^66 + 5*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 34*x^7 + 72*x^6 + 122*x^5 + 76*x^4 + 45*x^3 + 104*x^2 + 109*x + 10, x^75 + 41*x^73 + 38*x^72 + 82*x^71 + 72*x^70 + 42*x^69 + 4*x^68 + 85*x^67 + 72*x^66 + 85*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 18*x^7 + 72*x^6 + 106*x^5 + 4*x^4 + 125*x^3 + 72*x^2 + 61*x + 102, x^75 + 41*x^73 + 78*x^72 + 34*x^71 + 8*x^70 + 26*x^69 + 116*x^68 + 5*x^67 + 8*x^66 + 101*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 98*x^7 + 8*x^6 + 90*x^5 + 116*x^4 + 45*x^3 + 8*x^2 + 77*x + 78, x^75 + 41*x^73 + 74*x^72 + 82*x^71 + 88*x^70 + 42*x^69 + 124*x^68 + 85*x^67 + 24*x^66 + 85*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 18*x^7 + 88*x^6 + 106*x^5 + 124*x^4 + 125*x^3 + 24*x^2 + 61*x + 42, x^75 + 41*x^73 + 46*x^72 + 50*x^71 + 56*x^70 + 42*x^69 + 36*x^68 + 53*x^67 + 24*x^66 + 21*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 114*x^7 + 56*x^6 + 106*x^5 + 36*x^4 + 93*x^3 + 24*x^2 + 125*x + 126, x^75 + 41*x^73 + 2*x^72 + 114*x^71 + 8*x^70 + 106*x^69 + 124*x^68 + 117*x^67 + 40*x^66 + 85*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 50*x^7 + 8*x^6 + 42*x^5 + 124*x^4 + 29*x^3 + 40*x^2 + 61*x + 50, x^75 + 41*x^73 + 102*x^72 + 66*x^71 + 56*x^70 + 90*x^69 + 116*x^68 + 37*x^67 + 24*x^66 + 101*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 2*x^7 + 56*x^6 + 26*x^5 + 116*x^4 + 77*x^3 + 24*x^2 + 77*x + 118, x^75 + 41*x^73 + 42*x^72 + 66*x^71 + 40*x^70 + 90*x^69 + 12*x^68 + 37*x^67 + 8*x^66 + 101*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 2*x^7 + 40*x^6 + 26*x^5 + 12*x^4 + 77*x^3 + 8*x^2 + 77*x + 122, x^75 + 41*x^73 + 14*x^72 + 18*x^71 + 56*x^70 + 10*x^69 + 100*x^68 + 85*x^67 + 24*x^66 + 53*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 82*x^7 + 56*x^6 + 74*x^5 + 100*x^4 + 125*x^3 + 24*x^2 + 29*x + 94, x^75 + 41*x^73 + 30*x^72 + 18*x^71 + 24*x^70 + 74*x^69 + 36*x^68 + 85*x^67 + 56*x^66 + 117*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 82*x^7 + 24*x^6 + 10*x^5 + 36*x^4 + 125*x^3 + 56*x^2 + 93*x + 14, x^75 + 41*x^73 + 26*x^72 + 114*x^71 + 24*x^70 + 74*x^69 + 92*x^68 + 53*x^67 + 88*x^66 + 53*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 50*x^7 + 24*x^6 + 10*x^5 + 92*x^4 + 93*x^3 + 88*x^2 + 29*x + 122, x^75 + 41*x^73 + 82*x^72 + 66*x^71 + 88*x^70 + 122*x^69 + 108*x^68 + 101*x^67 + 24*x^66 + 5*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 2*x^7 + 88*x^6 + 58*x^5 + 108*x^4 + 13*x^3 + 24*x^2 + 109*x + 50, x^75 + 41*x^73 + 78*x^72 + 114*x^71 + 56*x^70 + 42*x^69 + 36*x^68 + 117*x^67 + 24*x^66 + 21*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 50*x^7 + 56*x^6 + 106*x^5 + 36*x^4 + 29*x^3 + 24*x^2 + 125*x + 94, x^75 + 41*x^73 + 106*x^72 + 82*x^71 + 120*x^70 + 42*x^69 + 92*x^68 + 85*x^67 + 120*x^66 + 85*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 18*x^7 + 120*x^6 + 106*x^5 + 92*x^4 + 125*x^3 + 120*x^2 + 61*x + 42, x^75 + 41*x^73 + 118*x^72 + 82*x^71 + 104*x^70 + 42*x^69 + 68*x^68 + 85*x^67 + 40*x^66 + 85*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 18*x^7 + 104*x^6 + 106*x^5 + 68*x^4 + 125*x^3 + 40*x^2 + 61*x + 86, x^75 + 41*x^73 + 10*x^72 + 98*x^71 + 72*x^70 + 122*x^69 + 108*x^68 + 5*x^67 + 104*x^66 + 69*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 34*x^7 + 72*x^6 + 58*x^5 + 108*x^4 + 45*x^3 + 104*x^2 + 45*x + 58, x^75 + 41*x^73 + 90*x^72 + 98*x^71 + 40*x^70 + 122*x^69 + 108*x^68 + 5*x^67 + 8*x^66 + 69*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 34*x^7 + 40*x^6 + 58*x^5 + 108*x^4 + 45*x^3 + 8*x^2 + 45*x + 106, x^75 + 41*x^73 + 82*x^72 + 34*x^71 + 88*x^70 + 90*x^69 + 108*x^68 + 5*x^67 + 24*x^66 + 37*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 98*x^7 + 88*x^6 + 26*x^5 + 108*x^4 + 45*x^3 + 24*x^2 + 13*x + 50, x^75 + 41*x^73 + 126*x^72 + 98*x^71 + 40*x^70 + 90*x^69 + 116*x^68 + 69*x^67 + 104*x^66 + 37*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 34*x^7 + 40*x^6 + 26*x^5 + 116*x^4 + 109*x^3 + 104*x^2 + 13*x + 30, x^75 + 41*x^73 + 50*x^72 + 98*x^71 + 88*x^70 + 90*x^69 + 108*x^68 + 69*x^67 + 24*x^66 + 37*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 34*x^7 + 88*x^6 + 26*x^5 + 108*x^4 + 109*x^3 + 24*x^2 + 13*x + 82, x^75 + 41*x^73 + 50*x^72 + 50*x^71 + 40*x^70 + 42*x^69 + 124*x^68 + 53*x^67 + 8*x^66 + 21*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 114*x^7 + 40*x^6 + 106*x^5 + 124*x^4 + 93*x^3 + 8*x^2 + 125*x + 2, x^75 + 41*x^73 + 38*x^72 + 98*x^71 + 24*x^70 + 122*x^69 + 84*x^68 + 5*x^67 + 56*x^66 + 69*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 34*x^7 + 24*x^6 + 58*x^5 + 84*x^4 + 45*x^3 + 56*x^2 + 45*x + 86, x^75 + 41*x^73 + 110*x^72 + 82*x^71 + 120*x^70 + 10*x^69 + 36*x^68 + 21*x^67 + 88*x^66 + 53*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 18*x^7 + 120*x^6 + 74*x^5 + 36*x^4 + 61*x^3 + 88*x^2 + 29*x + 62, x^75 + 41*x^73 + 90*x^72 + 114*x^71 + 24*x^70 + 10*x^69 + 28*x^68 + 53*x^67 + 88*x^66 + 117*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 50*x^7 + 24*x^6 + 74*x^5 + 28*x^4 + 93*x^3 + 88*x^2 + 93*x + 122, x^75 + 41*x^73 + 106*x^72 + 34*x^71 + 8*x^70 + 58*x^69 + 108*x^68 + 69*x^67 + 40*x^66 + 5*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 98*x^7 + 8*x^6 + 122*x^5 + 108*x^4 + 109*x^3 + 40*x^2 + 109*x + 90, x^75 + 41*x^73 + 42*x^72 + 50*x^71 + 56*x^70 + 74*x^69 + 92*x^68 + 117*x^67 + 56*x^66 + 53*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 114*x^7 + 56*x^6 + 10*x^5 + 92*x^4 + 29*x^3 + 56*x^2 + 29*x + 106, x^75 + 41*x^73 + 38*x^72 + 82*x^71 + 72*x^70 + 106*x^69 + 68*x^68 + 85*x^67 + 72*x^66 + 21*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 18*x^7 + 72*x^6 + 42*x^5 + 68*x^4 + 125*x^3 + 72*x^2 + 125*x + 38, x^75 + 41*x^73 + 26*x^72 + 34*x^71 + 40*x^70 + 122*x^69 + 44*x^68 + 69*x^67 + 8*x^66 + 69*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 98*x^7 + 40*x^6 + 58*x^5 + 44*x^4 + 109*x^3 + 8*x^2 + 45*x + 106, x^75 + 41*x^73 + 106*x^72 + 18*x^71 + 24*x^70 + 42*x^69 + 60*x^68 + 21*x^67 + 88*x^66 + 85*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 82*x^7 + 24*x^6 + 106*x^5 + 60*x^4 + 61*x^3 + 88*x^2 + 61*x + 74, x^75 + 41*x^73 + 94*x^72 + 98*x^71 + 104*x^70 + 26*x^69 + 52*x^68 + 69*x^67 + 40*x^66 + 101*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 34*x^7 + 104*x^6 + 90*x^5 + 52*x^4 + 109*x^3 + 40*x^2 + 77*x + 126, x^75 + 41*x^73 + 102*x^72 + 50*x^71 + 72*x^70 + 10*x^69 + 4*x^68 + 117*x^67 + 72*x^66 + 117*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 114*x^7 + 72*x^6 + 74*x^5 + 4*x^4 + 29*x^3 + 72*x^2 + 93*x + 38, x^75 + 41*x^73 + 86*x^72 + 2*x^71 + 24*x^70 + 90*x^69 + 116*x^68 + 101*x^67 + 56*x^66 + 101*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 66*x^7 + 24*x^6 + 26*x^5 + 116*x^4 + 13*x^3 + 56*x^2 + 77*x + 6, x^75 + 41*x^73 + 66*x^72 + 114*x^71 + 104*x^70 + 106*x^69 + 92*x^68 + 117*x^67 + 72*x^66 + 85*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 50*x^7 + 104*x^6 + 42*x^5 + 92*x^4 + 29*x^3 + 72*x^2 + 61*x + 18, x^75 + 41*x^73 + 46*x^72 + 66*x^71 + 8*x^70 + 122*x^69 + 116*x^68 + 101*x^67 + 8*x^66 + 5*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 2*x^7 + 8*x^6 + 58*x^5 + 116*x^4 + 13*x^3 + 8*x^2 + 109*x + 110, x^75 + 41*x^73 + 102*x^72 + 98*x^71 + 56*x^70 + 122*x^69 + 116*x^68 + 5*x^67 + 24*x^66 + 69*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 34*x^7 + 56*x^6 + 58*x^5 + 116*x^4 + 45*x^3 + 24*x^2 + 45*x + 118, x^75 + 41*x^73 + 18*x^72 + 98*x^71 + 24*x^70 + 90*x^69 + 108*x^68 + 69*x^67 + 88*x^66 + 37*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 34*x^7 + 24*x^6 + 26*x^5 + 108*x^4 + 109*x^3 + 88*x^2 + 13*x + 114, x^75 + 41*x^73 + 50*x^72 + 34*x^71 + 24*x^70 + 26*x^69 + 44*x^68 + 5*x^67 + 88*x^66 + 101*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 98*x^7 + 24*x^6 + 90*x^5 + 44*x^4 + 45*x^3 + 88*x^2 + 77*x + 18, x^75 + 41*x^73 + 110*x^72 + 2*x^71 + 104*x^70 + 122*x^69 + 20*x^68 + 37*x^67 + 40*x^66 + 5*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 66*x^7 + 104*x^6 + 58*x^5 + 20*x^4 + 77*x^3 + 40*x^2 + 109*x + 14, x^75 + 41*x^73 + 98*x^72 + 114*x^71 + 8*x^70 + 42*x^69 + 124*x^68 + 117*x^67 + 40*x^66 + 21*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 50*x^7 + 8*x^6 + 106*x^5 + 124*x^4 + 29*x^3 + 40*x^2 + 125*x + 82, x^75 + 41*x^73 + 6*x^72 + 82*x^71 + 72*x^70 + 42*x^69 + 68*x^68 + 85*x^67 + 72*x^66 + 85*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 18*x^7 + 72*x^6 + 106*x^5 + 68*x^4 + 125*x^3 + 72*x^2 + 61*x + 70, x^75 + 41*x^73 + 122*x^72 + 114*x^71 + 88*x^70 + 10*x^69 + 28*x^68 + 53*x^67 + 24*x^66 + 117*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 50*x^7 + 88*x^6 + 74*x^5 + 28*x^4 + 93*x^3 + 24*x^2 + 93*x + 90, x^75 + 41*x^73 + 106*x^72 + 114*x^71 + 120*x^70 + 74*x^69 + 92*x^68 + 53*x^67 + 120*x^66 + 53*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 50*x^7 + 120*x^6 + 10*x^5 + 92*x^4 + 93*x^3 + 120*x^2 + 29*x + 42, x^75 + 41*x^73 + 110*x^72 + 114*x^71 + 88*x^70 + 106*x^69 + 68*x^68 + 117*x^67 + 120*x^66 + 85*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 50*x^7 + 88*x^6 + 42*x^5 + 68*x^4 + 29*x^3 + 120*x^2 + 61*x + 30, x^75 + 41*x^73 + 70*x^72 + 82*x^71 + 8*x^70 + 106*x^69 + 68*x^68 + 85*x^67 + 8*x^66 + 21*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 18*x^7 + 8*x^6 + 42*x^5 + 68*x^4 + 125*x^3 + 8*x^2 + 125*x + 6, x^75 + 41*x^73 + 126*x^72 + 66*x^71 + 104*x^70 + 122*x^69 + 116*x^68 + 101*x^67 + 40*x^66 + 5*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 2*x^7 + 104*x^6 + 58*x^5 + 116*x^4 + 13*x^3 + 40*x^2 + 109*x + 30, x^75 + 41*x^73 + 106*x^72 + 34*x^71 + 40*x^70 + 58*x^69 + 12*x^68 + 69*x^67 + 8*x^66 + 5*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 98*x^7 + 40*x^6 + 122*x^5 + 12*x^4 + 109*x^3 + 8*x^2 + 109*x + 58, x^75 + 41*x^73 + 50*x^72 + 82*x^71 + 104*x^70 + 10*x^69 + 124*x^68 + 21*x^67 + 72*x^66 + 53*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 18*x^7 + 104*x^6 + 74*x^5 + 124*x^4 + 61*x^3 + 72*x^2 + 29*x + 2, x^75 + 41*x^73 + 50*x^72 + 98*x^71 + 120*x^70 + 90*x^69 + 12*x^68 + 69*x^67 + 120*x^66 + 37*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 34*x^7 + 120*x^6 + 26*x^5 + 12*x^4 + 109*x^3 + 120*x^2 + 13*x + 50, x^75 + 41*x^73 + 82*x^72 + 34*x^71 + 88*x^70 + 26*x^69 + 44*x^68 + 5*x^67 + 24*x^66 + 101*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 98*x^7 + 88*x^6 + 90*x^5 + 44*x^4 + 45*x^3 + 24*x^2 + 77*x + 114, x^75 + 41*x^73 + 78*x^72 + 98*x^71 + 40*x^70 + 26*x^69 + 84*x^68 + 69*x^67 + 104*x^66 + 101*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 34*x^7 + 40*x^6 + 90*x^5 + 84*x^4 + 109*x^3 + 104*x^2 + 77*x + 110, x^75 + 41*x^73 + 62*x^72 + 18*x^71 + 88*x^70 + 74*x^69 + 36*x^68 + 85*x^67 + 120*x^66 + 117*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 82*x^7 + 88*x^6 + 10*x^5 + 36*x^4 + 125*x^3 + 120*x^2 + 93*x + 110, x^75 + 41*x^73 + 118*x^72 + 66*x^71 + 24*x^70 + 90*x^69 + 116*x^68 + 37*x^67 + 56*x^66 + 101*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 2*x^7 + 24*x^6 + 26*x^5 + 116*x^4 + 77*x^3 + 56*x^2 + 77*x + 102, x^75 + 41*x^73 + 106*x^72 + 98*x^71 + 72*x^70 + 122*x^69 + 44*x^68 + 5*x^67 + 104*x^66 + 69*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 34*x^7 + 72*x^6 + 58*x^5 + 44*x^4 + 45*x^3 + 104*x^2 + 45*x + 26, x^75 + 41*x^73 + 6*x^72 + 114*x^71 + 40*x^70 + 10*x^69 + 100*x^68 + 53*x^67 + 104*x^66 + 117*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 50*x^7 + 40*x^6 + 74*x^5 + 100*x^4 + 93*x^3 + 104*x^2 + 93*x + 38, x^75 + 41*x^73 + 42*x^72 + 50*x^71 + 88*x^70 + 10*x^69 + 60*x^68 + 117*x^67 + 24*x^66 + 117*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 114*x^7 + 88*x^6 + 74*x^5 + 60*x^4 + 29*x^3 + 24*x^2 + 93*x + 10, x^75 + 41*x^73 + 30*x^72 + 98*x^71 + 72*x^70 + 26*x^69 + 20*x^68 + 69*x^67 + 72*x^66 + 101*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 34*x^7 + 72*x^6 + 90*x^5 + 20*x^4 + 109*x^3 + 72*x^2 + 77*x + 94, x^75 + 41*x^73 + 82*x^72 + 114*x^71 + 40*x^70 + 42*x^69 + 124*x^68 + 117*x^67 + 8*x^66 + 21*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 50*x^7 + 40*x^6 + 106*x^5 + 124*x^4 + 29*x^3 + 8*x^2 + 125*x + 98, x^75 + 41*x^73 + 38*x^72 + 34*x^71 + 88*x^70 + 122*x^69 + 84*x^68 + 69*x^67 + 120*x^66 + 69*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 98*x^7 + 88*x^6 + 58*x^5 + 84*x^4 + 109*x^3 + 120*x^2 + 45*x + 86, x^75 + 41*x^73 + 30*x^72 + 114*x^71 + 88*x^70 + 106*x^69 + 36*x^68 + 117*x^67 + 120*x^66 + 85*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 50*x^7 + 88*x^6 + 42*x^5 + 36*x^4 + 29*x^3 + 120*x^2 + 61*x + 14, x^75 + 41*x^73 + 118*x^72 + 50*x^71 + 8*x^70 + 10*x^69 + 100*x^68 + 117*x^67 + 8*x^66 + 117*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 114*x^7 + 8*x^6 + 74*x^5 + 100*x^4 + 29*x^3 + 8*x^2 + 93*x + 54, x^75 + 41*x^73 + 98*x^72 + 34*x^71 + 120*x^70 + 90*x^69 + 44*x^68 + 5*x^67 + 120*x^66 + 37*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 98*x^7 + 120*x^6 + 26*x^5 + 44*x^4 + 45*x^3 + 120*x^2 + 13*x + 98, x^75 + 41*x^73 + 46*x^72 + 66*x^71 + 104*x^70 + 58*x^69 + 20*x^68 + 101*x^67 + 40*x^66 + 69*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 2*x^7 + 104*x^6 + 122*x^5 + 20*x^4 + 13*x^3 + 40*x^2 + 45*x + 78, x^75 + 41*x^73 + 30*x^72 + 34*x^71 + 104*x^70 + 90*x^69 + 52*x^68 + 5*x^67 + 40*x^66 + 37*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 98*x^7 + 104*x^6 + 26*x^5 + 52*x^4 + 45*x^3 + 40*x^2 + 13*x + 62, x^75 + 41*x^73 + 98*x^72 + 66*x^71 + 88*x^70 + 58*x^69 + 76*x^68 + 101*x^67 + 24*x^66 + 69*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 2*x^7 + 88*x^6 + 122*x^5 + 76*x^4 + 13*x^3 + 24*x^2 + 45*x + 66, x^75 + 41*x^73 + 94*x^72 + 34*x^71 + 8*x^70 + 90*x^69 + 84*x^68 + 5*x^67 + 8*x^66 + 37*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 98*x^7 + 8*x^6 + 26*x^5 + 84*x^4 + 45*x^3 + 8*x^2 + 13*x + 94, x^75 + 41*x^73 + 10*x^72 + 34*x^71 + 8*x^70 + 122*x^69 + 108*x^68 + 69*x^67 + 40*x^66 + 69*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 98*x^7 + 8*x^6 + 58*x^5 + 108*x^4 + 109*x^3 + 40*x^2 + 45*x + 58, x^75 + 41*x^73 + 118*x^72 + 2*x^71 + 120*x^70 + 90*x^69 + 20*x^68 + 101*x^67 + 88*x^66 + 101*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 66*x^7 + 120*x^6 + 26*x^5 + 20*x^4 + 13*x^3 + 88*x^2 + 77*x + 70, x^75 + 41*x^73 + 46*x^72 + 98*x^71 + 104*x^70 + 26*x^69 + 84*x^68 + 69*x^67 + 40*x^66 + 101*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 34*x^7 + 104*x^6 + 90*x^5 + 84*x^4 + 109*x^3 + 40*x^2 + 77*x + 14, x^75 + 41*x^73 + 94*x^72 + 34*x^71 + 104*x^70 + 90*x^69 + 52*x^68 + 5*x^67 + 40*x^66 + 37*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 98*x^7 + 104*x^6 + 26*x^5 + 52*x^4 + 45*x^3 + 40*x^2 + 13*x + 126, x^75 + 41*x^73 + 82*x^72 + 82*x^71 + 8*x^70 + 10*x^69 + 92*x^68 + 21*x^67 + 40*x^66 + 53*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 18*x^7 + 8*x^6 + 74*x^5 + 92*x^4 + 61*x^3 + 40*x^2 + 29*x + 2, x^75 + 41*x^73 + 86*x^72 + 98*x^71 + 120*x^70 + 122*x^69 + 20*x^68 + 5*x^67 + 88*x^66 + 69*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 34*x^7 + 120*x^6 + 58*x^5 + 20*x^4 + 45*x^3 + 88*x^2 + 45*x + 102, x^75 + 41*x^73 + 2*x^72 + 2*x^71 + 88*x^70 + 122*x^69 + 12*x^68 + 37*x^67 + 24*x^66 + 5*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 66*x^7 + 88*x^6 + 58*x^5 + 12*x^4 + 77*x^3 + 24*x^2 + 109*x + 98, x^75 + 41*x^73 + 74*x^72 + 34*x^71 + 8*x^70 + 58*x^69 + 44*x^68 + 69*x^67 + 40*x^66 + 5*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 98*x^7 + 8*x^6 + 122*x^5 + 44*x^4 + 109*x^3 + 40*x^2 + 109*x + 58, x^75 + 41*x^73 + 98*x^72 + 50*x^71 + 72*x^70 + 106*x^69 + 60*x^68 + 53*x^67 + 104*x^66 + 85*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 114*x^7 + 72*x^6 + 42*x^5 + 60*x^4 + 93*x^3 + 104*x^2 + 61*x + 18, x^75 + 41*x^73 + 98*x^72 + 34*x^71 + 56*x^70 + 26*x^69 + 44*x^68 + 5*x^67 + 56*x^66 + 101*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 98*x^7 + 56*x^6 + 90*x^5 + 44*x^4 + 45*x^3 + 56*x^2 + 77*x + 98, x^75 + 41*x^73 + 22*x^72 + 50*x^71 + 72*x^70 + 10*x^69 + 100*x^68 + 117*x^67 + 72*x^66 + 117*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 114*x^7 + 72*x^6 + 74*x^5 + 100*x^4 + 29*x^3 + 72*x^2 + 93*x + 22, x^75 + 41*x^73 + 62*x^72 + 2*x^71 + 40*x^70 + 122*x^69 + 116*x^68 + 37*x^67 + 104*x^66 + 5*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 66*x^7 + 40*x^6 + 58*x^5 + 116*x^4 + 77*x^3 + 104*x^2 + 109*x + 94, x^75 + 41*x^73 + 70*x^72 + 98*x^71 + 120*x^70 + 58*x^69 + 52*x^68 + 5*x^67 + 88*x^66 + 5*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 34*x^7 + 120*x^6 + 122*x^5 + 52*x^4 + 45*x^3 + 88*x^2 + 109*x + 86, x^75 + 41*x^73 + 90*x^72 + 2*x^71 + 40*x^70 + 90*x^69 + 44*x^68 + 101*x^67 + 8*x^66 + 101*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 66*x^7 + 40*x^6 + 26*x^5 + 44*x^4 + 13*x^3 + 8*x^2 + 77*x + 42, x^75 + 41*x^73 + 106*x^72 + 114*x^71 + 24*x^70 + 74*x^69 + 124*x^68 + 53*x^67 + 88*x^66 + 53*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 50*x^7 + 24*x^6 + 10*x^5 + 124*x^4 + 93*x^3 + 88*x^2 + 29*x + 10, x^75 + 41*x^73 + 94*x^72 + 2*x^71 + 72*x^70 + 58*x^69 + 20*x^68 + 37*x^67 + 72*x^66 + 69*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 66*x^7 + 72*x^6 + 122*x^5 + 20*x^4 + 77*x^3 + 72*x^2 + 45*x + 30, x^75 + 41*x^73 + 118*x^72 + 18*x^71 + 8*x^70 + 42*x^69 + 36*x^68 + 21*x^67 + 8*x^66 + 85*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 82*x^7 + 8*x^6 + 106*x^5 + 36*x^4 + 61*x^3 + 8*x^2 + 61*x + 118, x^75 + 41*x^73 + 110*x^72 + 66*x^71 + 72*x^70 + 122*x^69 + 52*x^68 + 101*x^67 + 72*x^66 + 5*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 2*x^7 + 72*x^6 + 58*x^5 + 52*x^4 + 13*x^3 + 72*x^2 + 109*x + 110, x^75 + 41*x^73 + 46*x^72 + 82*x^71 + 56*x^70 + 10*x^69 + 100*x^68 + 21*x^67 + 24*x^66 + 53*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 18*x^7 + 56*x^6 + 74*x^5 + 100*x^4 + 61*x^3 + 24*x^2 + 29*x + 62, x^75 + 41*x^73 + 62*x^72 + 98*x^71 + 8*x^70 + 26*x^69 + 20*x^68 + 69*x^67 + 8*x^66 + 101*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 34*x^7 + 8*x^6 + 90*x^5 + 20*x^4 + 109*x^3 + 8*x^2 + 77*x + 62, x^75 + 41*x^73 + 14*x^72 + 114*x^71 + 120*x^70 + 106*x^69 + 36*x^68 + 117*x^67 + 88*x^66 + 85*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 50*x^7 + 120*x^6 + 42*x^5 + 36*x^4 + 29*x^3 + 88*x^2 + 61*x + 30, x^75 + 41*x^73 + 18*x^72 + 98*x^71 + 24*x^70 + 26*x^69 + 44*x^68 + 69*x^67 + 88*x^66 + 101*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 34*x^7 + 24*x^6 + 90*x^5 + 44*x^4 + 109*x^3 + 88*x^2 + 77*x + 50, x^75 + 41*x^73 + 14*x^72 + 98*x^71 + 40*x^70 + 90*x^69 + 20*x^68 + 69*x^67 + 104*x^66 + 37*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 34*x^7 + 40*x^6 + 26*x^5 + 20*x^4 + 109*x^3 + 104*x^2 + 13*x + 110, x^75 + 41*x^73 + 30*x^72 + 82*x^71 + 120*x^70 + 10*x^69 + 4*x^68 + 21*x^67 + 88*x^66 + 53*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 18*x^7 + 120*x^6 + 74*x^5 + 4*x^4 + 61*x^3 + 88*x^2 + 29*x + 46, x^75 + 41*x^73 + 86*x^72 + 82*x^71 + 40*x^70 + 106*x^69 + 4*x^68 + 85*x^67 + 104*x^66 + 21*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 18*x^7 + 40*x^6 + 42*x^5 + 4*x^4 + 125*x^3 + 104*x^2 + 125*x + 54, x^75 + 41*x^73 + 46*x^72 + 66*x^71 + 40*x^70 + 122*x^69 + 20*x^68 + 101*x^67 + 104*x^66 + 5*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 2*x^7 + 40*x^6 + 58*x^5 + 20*x^4 + 13*x^3 + 104*x^2 + 109*x + 78, x^75 + 41*x^73 + 34*x^72 + 114*x^71 + 40*x^70 + 106*x^69 + 92*x^68 + 117*x^67 + 8*x^66 + 85*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 50*x^7 + 40*x^6 + 42*x^5 + 92*x^4 + 29*x^3 + 8*x^2 + 61*x + 50, x^75 + 41*x^73 + 110*x^72 + 66*x^71 + 40*x^70 + 58*x^69 + 84*x^68 + 101*x^67 + 104*x^66 + 69*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 2*x^7 + 40*x^6 + 122*x^5 + 84*x^4 + 13*x^3 + 104*x^2 + 45*x + 78, x^75 + 41*x^73 + 122*x^72 + 2*x^71 + 40*x^70 + 26*x^69 + 44*x^68 + 101*x^67 + 8*x^66 + 37*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 66*x^7 + 40*x^6 + 90*x^5 + 44*x^4 + 13*x^3 + 8*x^2 + 13*x + 10, x^75 + 41*x^73 + 126*x^72 + 18*x^71 + 88*x^70 + 74*x^69 + 36*x^68 + 85*x^67 + 120*x^66 + 117*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 82*x^7 + 88*x^6 + 10*x^5 + 36*x^4 + 125*x^3 + 120*x^2 + 93*x + 46, x^75 + 41*x^73 + 6*x^72 + 82*x^71 + 40*x^70 + 106*x^69 + 100*x^68 + 85*x^67 + 104*x^66 + 21*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 18*x^7 + 40*x^6 + 42*x^5 + 100*x^4 + 125*x^3 + 104*x^2 + 125*x + 38, x^75 + 41*x^73 + 18*x^72 + 34*x^71 + 56*x^70 + 26*x^69 + 12*x^68 + 5*x^67 + 56*x^66 + 101*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 98*x^7 + 56*x^6 + 90*x^5 + 12*x^4 + 45*x^3 + 56*x^2 + 77*x + 82, x^75 + 41*x^73 + 106*x^72 + 34*x^71 + 8*x^70 + 122*x^69 + 44*x^68 + 69*x^67 + 40*x^66 + 69*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 98*x^7 + 8*x^6 + 58*x^5 + 44*x^4 + 109*x^3 + 40*x^2 + 45*x + 26, x^75 + 41*x^73 + 10*x^72 + 82*x^71 + 88*x^70 + 106*x^69 + 60*x^68 + 85*x^67 + 24*x^66 + 21*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 18*x^7 + 88*x^6 + 42*x^5 + 60*x^4 + 125*x^3 + 24*x^2 + 125*x + 42, x^75 + 41*x^73 + 22*x^72 + 50*x^71 + 104*x^70 + 10*x^69 + 4*x^68 + 117*x^67 + 40*x^66 + 117*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 114*x^7 + 104*x^6 + 74*x^5 + 4*x^4 + 29*x^3 + 40*x^2 + 93*x + 118, x^75 + 41*x^73 + 126*x^72 + 98*x^71 + 104*x^70 + 26*x^69 + 116*x^68 + 69*x^67 + 40*x^66 + 101*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 34*x^7 + 104*x^6 + 90*x^5 + 116*x^4 + 109*x^3 + 40*x^2 + 77*x + 30, x^75 + 41*x^73 + 6*x^72 + 2*x^71 + 88*x^70 + 90*x^69 + 20*x^68 + 101*x^67 + 120*x^66 + 101*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 66*x^7 + 88*x^6 + 26*x^5 + 20*x^4 + 13*x^3 + 120*x^2 + 77*x + 54, x^75 + 41*x^73 + 58*x^72 + 114*x^71 + 24*x^70 + 74*x^69 + 28*x^68 + 53*x^67 + 88*x^66 + 53*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 50*x^7 + 24*x^6 + 10*x^5 + 28*x^4 + 93*x^3 + 88*x^2 + 29*x + 26, x^75 + 41*x^73 + 114*x^72 + 114*x^71 + 104*x^70 + 106*x^69 + 60*x^68 + 117*x^67 + 72*x^66 + 85*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 50*x^7 + 104*x^6 + 42*x^5 + 60*x^4 + 29*x^3 + 72*x^2 + 61*x + 2, x^75 + 41*x^73 + 114*x^72 + 50*x^71 + 104*x^70 + 106*x^69 + 124*x^68 + 53*x^67 + 72*x^66 + 85*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 114*x^7 + 104*x^6 + 42*x^5 + 124*x^4 + 93*x^3 + 72*x^2 + 61*x + 66, x^75 + 41*x^73 + 106*x^72 + 2*x^71 + 104*x^70 + 26*x^69 + 76*x^68 + 101*x^67 + 72*x^66 + 37*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 66*x^7 + 104*x^6 + 90*x^5 + 76*x^4 + 13*x^3 + 72*x^2 + 13*x + 122, x^75 + 41*x^73 + 30*x^72 + 34*x^71 + 72*x^70 + 26*x^69 + 84*x^68 + 5*x^67 + 72*x^66 + 101*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 98*x^7 + 72*x^6 + 90*x^5 + 84*x^4 + 45*x^3 + 72*x^2 + 77*x + 30, x^75 + 41*x^73 + 6*x^72 + 34*x^71 + 120*x^70 + 58*x^69 + 116*x^68 + 69*x^67 + 88*x^66 + 5*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 98*x^7 + 120*x^6 + 122*x^5 + 116*x^4 + 109*x^3 + 88*x^2 + 109*x + 86, x^75 + 41*x^73 + 118*x^72 + 18*x^71 + 72*x^70 + 106*x^69 + 36*x^68 + 21*x^67 + 72*x^66 + 21*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 82*x^7 + 72*x^6 + 42*x^5 + 36*x^4 + 61*x^3 + 72*x^2 + 125*x + 118, x^75 + 41*x^73 + 30*x^72 + 50*x^71 + 56*x^70 + 42*x^69 + 4*x^68 + 53*x^67 + 24*x^66 + 21*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 114*x^7 + 56*x^6 + 106*x^5 + 4*x^4 + 93*x^3 + 24*x^2 + 125*x + 46, x^75 + 41*x^73 + 10*x^72 + 50*x^71 + 56*x^70 + 10*x^69 + 92*x^68 + 117*x^67 + 56*x^66 + 117*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 114*x^7 + 56*x^6 + 74*x^5 + 92*x^4 + 29*x^3 + 56*x^2 + 93*x + 10, x^75 + 41*x^73 + 26*x^72 + 18*x^71 + 24*x^70 + 106*x^69 + 92*x^68 + 21*x^67 + 88*x^66 + 21*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 82*x^7 + 24*x^6 + 42*x^5 + 92*x^4 + 61*x^3 + 88*x^2 + 125*x + 122, x^75 + 41*x^73 + 106*x^72 + 82*x^71 + 88*x^70 + 106*x^69 + 124*x^68 + 85*x^67 + 24*x^66 + 21*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 18*x^7 + 88*x^6 + 42*x^5 + 124*x^4 + 125*x^3 + 24*x^2 + 125*x + 10, x^75 + 41*x^73 + 102*x^72 + 82*x^71 + 8*x^70 + 42*x^69 + 68*x^68 + 85*x^67 + 8*x^66 + 85*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 18*x^7 + 8*x^6 + 106*x^5 + 68*x^4 + 125*x^3 + 8*x^2 + 61*x + 102, x^75 + 41*x^73 + 126*x^72 + 114*x^71 + 56*x^70 + 42*x^69 + 4*x^68 + 117*x^67 + 24*x^66 + 21*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 50*x^7 + 56*x^6 + 106*x^5 + 4*x^4 + 29*x^3 + 24*x^2 + 125*x + 78, x^75 + 41*x^73 + 2*x^72 + 34*x^71 + 88*x^70 + 26*x^69 + 12*x^68 + 5*x^67 + 24*x^66 + 101*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 98*x^7 + 88*x^6 + 90*x^5 + 12*x^4 + 45*x^3 + 24*x^2 + 77*x + 98, x^75 + 41*x^73 + 106*x^72 + 114*x^71 + 56*x^70 + 74*x^69 + 28*x^68 + 53*x^67 + 56*x^66 + 53*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 50*x^7 + 56*x^6 + 10*x^5 + 28*x^4 + 93*x^3 + 56*x^2 + 29*x + 106, x^75 + 41*x^73 + 30*x^72 + 66*x^71 + 72*x^70 + 122*x^69 + 20*x^68 + 101*x^67 + 72*x^66 + 5*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 2*x^7 + 72*x^6 + 58*x^5 + 20*x^4 + 13*x^3 + 72*x^2 + 109*x + 94, x^75 + 41*x^73 + 54*x^72 + 98*x^71 + 56*x^70 + 58*x^69 + 84*x^68 + 5*x^67 + 24*x^66 + 5*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 34*x^7 + 56*x^6 + 122*x^5 + 84*x^4 + 45*x^3 + 24*x^2 + 109*x + 70, x^75 + 41*x^73 + 62*x^72 + 114*x^71 + 56*x^70 + 42*x^69 + 4*x^68 + 117*x^67 + 24*x^66 + 21*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 50*x^7 + 56*x^6 + 106*x^5 + 4*x^4 + 29*x^3 + 24*x^2 + 125*x + 14, x^75 + 41*x^73 + 66*x^72 + 114*x^71 + 104*x^70 + 42*x^69 + 28*x^68 + 117*x^67 + 72*x^66 + 21*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 50*x^7 + 104*x^6 + 106*x^5 + 28*x^4 + 29*x^3 + 72*x^2 + 125*x + 82, x^75 + 41*x^73 + 34*x^72 + 50*x^71 + 40*x^70 + 106*x^69 + 28*x^68 + 53*x^67 + 8*x^66 + 85*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 114*x^7 + 40*x^6 + 42*x^5 + 28*x^4 + 93*x^3 + 8*x^2 + 61*x + 114, x^75 + 41*x^73 + 54*x^72 + 18*x^71 + 8*x^70 + 106*x^69 + 100*x^68 + 21*x^67 + 8*x^66 + 21*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 82*x^7 + 8*x^6 + 42*x^5 + 100*x^4 + 61*x^3 + 8*x^2 + 125*x + 118, x^75 + 41*x^73 + 66*x^72 + 18*x^71 + 72*x^70 + 74*x^69 + 124*x^68 + 85*x^67 + 104*x^66 + 117*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 82*x^7 + 72*x^6 + 10*x^5 + 124*x^4 + 125*x^3 + 104*x^2 + 93*x + 114, x^75 + 41*x^73 + 38*x^72 + 50*x^71 + 40*x^70 + 74*x^69 + 36*x^68 + 117*x^67 + 104*x^66 + 53*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 114*x^7 + 40*x^6 + 10*x^5 + 36*x^4 + 29*x^3 + 104*x^2 + 29*x + 70, x^75 + 41*x^73 + 114*x^72 + 2*x^71 + 120*x^70 + 122*x^69 + 12*x^68 + 37*x^67 + 120*x^66 + 5*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 66*x^7 + 120*x^6 + 58*x^5 + 12*x^4 + 77*x^3 + 120*x^2 + 109*x + 114, x^75 + 41*x^73 + 110*x^72 + 82*x^71 + 56*x^70 + 74*x^69 + 36*x^68 + 21*x^67 + 24*x^66 + 117*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 18*x^7 + 56*x^6 + 10*x^5 + 36*x^4 + 61*x^3 + 24*x^2 + 93*x + 62, x^75 + 41*x^73 + 14*x^72 + 34*x^71 + 8*x^70 + 90*x^69 + 52*x^68 + 5*x^67 + 8*x^66 + 37*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 98*x^7 + 8*x^6 + 26*x^5 + 52*x^4 + 45*x^3 + 8*x^2 + 13*x + 78, x^75 + 41*x^73 + 122*x^72 + 98*x^71 + 8*x^70 + 122*x^69 + 12*x^68 + 5*x^67 + 40*x^66 + 69*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 34*x^7 + 8*x^6 + 58*x^5 + 12*x^4 + 45*x^3 + 40*x^2 + 45*x + 42, x^75 + 41*x^73 + 42*x^72 + 34*x^71 + 104*x^70 + 122*x^69 + 12*x^68 + 69*x^67 + 72*x^66 + 69*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 98*x^7 + 104*x^6 + 58*x^5 + 12*x^4 + 109*x^3 + 72*x^2 + 45*x + 122, x^75 + 41*x^73 + 86*x^72 + 34*x^71 + 24*x^70 + 58*x^69 + 52*x^68 + 69*x^67 + 56*x^66 + 5*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 98*x^7 + 24*x^6 + 122*x^5 + 52*x^4 + 109*x^3 + 56*x^2 + 109*x + 70, x^75 + 41*x^73 + 126*x^72 + 2*x^71 + 40*x^70 + 122*x^69 + 116*x^68 + 37*x^67 + 104*x^66 + 5*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 66*x^7 + 40*x^6 + 58*x^5 + 116*x^4 + 77*x^3 + 104*x^2 + 109*x + 30, x^75 + 41*x^73 + 66*x^72 + 66*x^71 + 88*x^70 + 122*x^69 + 76*x^68 + 101*x^67 + 24*x^66 + 5*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 2*x^7 + 88*x^6 + 58*x^5 + 76*x^4 + 13*x^3 + 24*x^2 + 109*x + 98, x^75 + 41*x^73 + 26*x^72 + 50*x^71 + 120*x^70 + 74*x^69 + 124*x^68 + 117*x^67 + 120*x^66 + 53*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 114*x^7 + 120*x^6 + 10*x^5 + 124*x^4 + 29*x^3 + 120*x^2 + 29*x + 90, x^75 + 41*x^73 + 50*x^72 + 2*x^71 + 88*x^70 + 122*x^69 + 108*x^68 + 37*x^67 + 24*x^66 + 5*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 66*x^7 + 88*x^6 + 58*x^5 + 108*x^4 + 77*x^3 + 24*x^2 + 109*x + 82, x^75 + 41*x^73 + 94*x^72 + 66*x^71 + 72*x^70 + 58*x^69 + 84*x^68 + 101*x^67 + 72*x^66 + 69*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 2*x^7 + 72*x^6 + 122*x^5 + 84*x^4 + 13*x^3 + 72*x^2 + 45*x + 94, x^75 + 41*x^73 + 82*x^72 + 114*x^71 + 104*x^70 + 42*x^69 + 60*x^68 + 117*x^67 + 72*x^66 + 21*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 50*x^7 + 104*x^6 + 106*x^5 + 60*x^4 + 29*x^3 + 72*x^2 + 125*x + 34, x^75 + 41*x^73 + 10*x^72 + 98*x^71 + 8*x^70 + 58*x^69 + 108*x^68 + 5*x^67 + 40*x^66 + 5*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 34*x^7 + 8*x^6 + 122*x^5 + 108*x^4 + 45*x^3 + 40*x^2 + 109*x + 58, x^75 + 41*x^73 + 34*x^72 + 114*x^71 + 72*x^70 + 42*x^69 + 60*x^68 + 117*x^67 + 104*x^66 + 21*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 50*x^7 + 72*x^6 + 106*x^5 + 60*x^4 + 29*x^3 + 104*x^2 + 125*x + 82, x^75 + 41*x^73 + 6*x^72 + 2*x^71 + 24*x^70 + 26*x^69 + 20*x^68 + 101*x^67 + 56*x^66 + 37*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 66*x^7 + 24*x^6 + 90*x^5 + 20*x^4 + 13*x^3 + 56*x^2 + 13*x + 54, x^75 + 41*x^73 + 90*x^72 + 34*x^71 + 72*x^70 + 122*x^69 + 76*x^68 + 69*x^67 + 104*x^66 + 69*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 98*x^7 + 72*x^6 + 58*x^5 + 76*x^4 + 109*x^3 + 104*x^2 + 45*x + 10, x^75 + 41*x^73 + 110*x^72 + 114*x^71 + 120*x^70 + 42*x^69 + 36*x^68 + 117*x^67 + 88*x^66 + 21*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 50*x^7 + 120*x^6 + 106*x^5 + 36*x^4 + 29*x^3 + 88*x^2 + 125*x + 62, x^75 + 41*x^73 + 50*x^72 + 66*x^71 + 24*x^70 + 122*x^69 + 108*x^68 + 101*x^67 + 88*x^66 + 5*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 2*x^7 + 24*x^6 + 58*x^5 + 108*x^4 + 13*x^3 + 88*x^2 + 109*x + 82, x^75 + 41*x^73 + 42*x^72 + 50*x^71 + 56*x^70 + 10*x^69 + 28*x^68 + 117*x^67 + 56*x^66 + 117*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 114*x^7 + 56*x^6 + 74*x^5 + 28*x^4 + 29*x^3 + 56*x^2 + 93*x + 42, x^75 + 41*x^73 + 78*x^72 + 34*x^71 + 72*x^70 + 26*x^69 + 52*x^68 + 5*x^67 + 72*x^66 + 101*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 98*x^7 + 72*x^6 + 90*x^5 + 52*x^4 + 45*x^3 + 72*x^2 + 77*x + 14, x^75 + 41*x^73 + 86*x^72 + 34*x^71 + 56*x^70 + 122*x^69 + 20*x^68 + 69*x^67 + 24*x^66 + 69*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 98*x^7 + 56*x^6 + 58*x^5 + 20*x^4 + 109*x^3 + 24*x^2 + 45*x + 102, x^75 + 41*x^73 + 126*x^72 + 50*x^71 + 56*x^70 + 106*x^69 + 4*x^68 + 53*x^67 + 24*x^66 + 85*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 114*x^7 + 56*x^6 + 42*x^5 + 4*x^4 + 93*x^3 + 24*x^2 + 61*x + 78, x^75 + 41*x^73 + 106*x^72 + 82*x^71 + 24*x^70 + 106*x^69 + 60*x^68 + 85*x^67 + 88*x^66 + 21*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 18*x^7 + 24*x^6 + 42*x^5 + 60*x^4 + 125*x^3 + 88*x^2 + 125*x + 74, x^75 + 41*x^73 + 74*x^72 + 66*x^71 + 40*x^70 + 90*x^69 + 76*x^68 + 37*x^67 + 8*x^66 + 101*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 2*x^7 + 40*x^6 + 26*x^5 + 76*x^4 + 77*x^3 + 8*x^2 + 77*x + 26, x^75 + 41*x^73 + 54*x^72 + 34*x^71 + 120*x^70 + 58*x^69 + 84*x^68 + 69*x^67 + 88*x^66 + 5*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 98*x^7 + 120*x^6 + 122*x^5 + 84*x^4 + 109*x^3 + 88*x^2 + 109*x + 70, x^75 + 41*x^73 + 42*x^72 + 18*x^71 + 88*x^70 + 106*x^69 + 60*x^68 + 21*x^67 + 24*x^66 + 21*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 82*x^7 + 88*x^6 + 42*x^5 + 60*x^4 + 61*x^3 + 24*x^2 + 125*x + 10, x^75 + 41*x^73 + 94*x^72 + 66*x^71 + 8*x^70 + 58*x^69 + 20*x^68 + 101*x^67 + 8*x^66 + 69*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 2*x^7 + 8*x^6 + 122*x^5 + 20*x^4 + 13*x^3 + 8*x^2 + 45*x + 30, x^75 + 41*x^73 + 66*x^72 + 114*x^71 + 40*x^70 + 42*x^69 + 92*x^68 + 117*x^67 + 8*x^66 + 21*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 50*x^7 + 40*x^6 + 106*x^5 + 92*x^4 + 29*x^3 + 8*x^2 + 125*x + 18, x^75 + 41*x^73 + 114*x^72 + 18*x^71 + 8*x^70 + 74*x^69 + 28*x^68 + 85*x^67 + 40*x^66 + 117*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 82*x^7 + 8*x^6 + 10*x^5 + 28*x^4 + 125*x^3 + 40*x^2 + 93*x + 34, x^75 + 41*x^73 + 66*x^72 + 66*x^71 + 120*x^70 + 122*x^69 + 108*x^68 + 101*x^67 + 120*x^66 + 5*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 2*x^7 + 120*x^6 + 58*x^5 + 108*x^4 + 13*x^3 + 120*x^2 + 109*x + 66, x^75 + 41*x^73 + 102*x^72 + 2*x^71 + 24*x^70 + 90*x^69 + 20*x^68 + 101*x^67 + 56*x^66 + 101*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 66*x^7 + 24*x^6 + 26*x^5 + 20*x^4 + 13*x^3 + 56*x^2 + 77*x + 86, x^75 + 41*x^73 + 38*x^72 + 50*x^71 + 72*x^70 + 10*x^69 + 4*x^68 + 117*x^67 + 72*x^66 + 117*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 114*x^7 + 72*x^6 + 74*x^5 + 4*x^4 + 29*x^3 + 72*x^2 + 93*x + 102, x^75 + 41*x^73 + 2*x^72 + 98*x^71 + 56*x^70 + 26*x^69 + 44*x^68 + 69*x^67 + 56*x^66 + 101*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 34*x^7 + 56*x^6 + 90*x^5 + 44*x^4 + 109*x^3 + 56*x^2 + 77*x + 66, x^75 + 41*x^73 + 122*x^72 + 66*x^71 + 104*x^70 + 26*x^69 + 44*x^68 + 37*x^67 + 72*x^66 + 37*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 2*x^7 + 104*x^6 + 90*x^5 + 44*x^4 + 77*x^3 + 72*x^2 + 13*x + 10, x^75 + 41*x^73 + 94*x^72 + 114*x^71 + 56*x^70 + 106*x^69 + 4*x^68 + 117*x^67 + 24*x^66 + 85*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 50*x^7 + 56*x^6 + 42*x^5 + 4*x^4 + 29*x^3 + 24*x^2 + 61*x + 110, x^75 + 41*x^73 + 86*x^72 + 50*x^71 + 40*x^70 + 10*x^69 + 68*x^68 + 117*x^67 + 104*x^66 + 117*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 114*x^7 + 40*x^6 + 74*x^5 + 68*x^4 + 29*x^3 + 104*x^2 + 93*x + 118, x^75 + 41*x^73 + 18*x^72 + 2*x^71 + 24*x^70 + 122*x^69 + 108*x^68 + 37*x^67 + 88*x^66 + 5*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 66*x^7 + 24*x^6 + 58*x^5 + 108*x^4 + 77*x^3 + 88*x^2 + 109*x + 114, x^75 + 41*x^73 + 6*x^72 + 114*x^71 + 104*x^70 + 10*x^69 + 36*x^68 + 53*x^67 + 40*x^66 + 117*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 50*x^7 + 104*x^6 + 74*x^5 + 36*x^4 + 93*x^3 + 40*x^2 + 93*x + 102, x^75 + 41*x^73 + 102*x^72 + 82*x^71 + 72*x^70 + 106*x^69 + 68*x^68 + 85*x^67 + 72*x^66 + 21*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 18*x^7 + 72*x^6 + 42*x^5 + 68*x^4 + 125*x^3 + 72*x^2 + 125*x + 102, x^75 + 41*x^73 + 110*x^72 + 98*x^71 + 104*x^70 + 26*x^69 + 84*x^68 + 69*x^67 + 40*x^66 + 101*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 34*x^7 + 104*x^6 + 90*x^5 + 84*x^4 + 109*x^3 + 40*x^2 + 77*x + 78, x^75 + 41*x^73 + 62*x^72 + 50*x^71 + 56*x^70 + 106*x^69 + 4*x^68 + 53*x^67 + 24*x^66 + 85*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 114*x^7 + 56*x^6 + 42*x^5 + 4*x^4 + 93*x^3 + 24*x^2 + 61*x + 14, x^75 + 41*x^73 + 62*x^72 + 2*x^71 + 104*x^70 + 58*x^69 + 116*x^68 + 37*x^67 + 40*x^66 + 69*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 66*x^7 + 104*x^6 + 122*x^5 + 116*x^4 + 77*x^3 + 40*x^2 + 45*x + 94, x^75 + 41*x^73 + 70*x^72 + 98*x^71 + 24*x^70 + 122*x^69 + 20*x^68 + 5*x^67 + 56*x^66 + 69*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 34*x^7 + 24*x^6 + 58*x^5 + 20*x^4 + 45*x^3 + 56*x^2 + 45*x + 118, x^75 + 41*x^73 + 102*x^72 + 82*x^71 + 104*x^70 + 42*x^69 + 36*x^68 + 85*x^67 + 40*x^66 + 85*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 18*x^7 + 104*x^6 + 106*x^5 + 36*x^4 + 125*x^3 + 40*x^2 + 61*x + 6, x^75 + 41*x^73 + 122*x^72 + 34*x^71 + 104*x^70 + 122*x^69 + 44*x^68 + 69*x^67 + 72*x^66 + 69*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 98*x^7 + 104*x^6 + 58*x^5 + 44*x^4 + 109*x^3 + 72*x^2 + 45*x + 10, x^75 + 41*x^73 + 70*x^72 + 66*x^71 + 24*x^70 + 90*x^69 + 20*x^68 + 37*x^67 + 56*x^66 + 101*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 2*x^7 + 24*x^6 + 26*x^5 + 20*x^4 + 77*x^3 + 56*x^2 + 77*x + 118, x^75 + 41*x^73 + 10*x^72 + 114*x^71 + 56*x^70 + 74*x^69 + 92*x^68 + 53*x^67 + 56*x^66 + 53*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 50*x^7 + 56*x^6 + 10*x^5 + 92*x^4 + 93*x^3 + 56*x^2 + 29*x + 10, x^75 + 41*x^73 + 22*x^72 + 82*x^71 + 104*x^70 + 106*x^69 + 68*x^68 + 85*x^67 + 40*x^66 + 21*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 18*x^7 + 104*x^6 + 42*x^5 + 68*x^4 + 125*x^3 + 40*x^2 + 125*x + 54, x^75 + 41*x^73 + 66*x^72 + 2*x^71 + 120*x^70 + 58*x^69 + 108*x^68 + 37*x^67 + 120*x^66 + 69*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 66*x^7 + 120*x^6 + 122*x^5 + 108*x^4 + 77*x^3 + 120*x^2 + 45*x + 66, x^75 + 41*x^73 + 118*x^72 + 50*x^71 + 8*x^70 + 74*x^69 + 36*x^68 + 117*x^67 + 8*x^66 + 53*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 114*x^7 + 8*x^6 + 10*x^5 + 36*x^4 + 29*x^3 + 8*x^2 + 29*x + 118, x^75 + 41*x^73 + 34*x^72 + 98*x^71 + 24*x^70 + 90*x^69 + 12*x^68 + 69*x^67 + 88*x^66 + 37*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 34*x^7 + 24*x^6 + 26*x^5 + 12*x^4 + 109*x^3 + 88*x^2 + 13*x + 66, x^75 + 41*x^73 + 122*x^72 + 50*x^71 + 120*x^70 + 10*x^69 + 124*x^68 + 117*x^67 + 120*x^66 + 117*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 114*x^7 + 120*x^6 + 74*x^5 + 124*x^4 + 29*x^3 + 120*x^2 + 93*x + 122, x^75 + 41*x^73 + 2*x^72 + 2*x^71 + 120*x^70 + 122*x^69 + 44*x^68 + 37*x^67 + 120*x^66 + 5*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 66*x^7 + 120*x^6 + 58*x^5 + 44*x^4 + 77*x^3 + 120*x^2 + 109*x + 66, x^75 + 41*x^73 + 46*x^72 + 34*x^71 + 8*x^70 + 90*x^69 + 116*x^68 + 5*x^67 + 8*x^66 + 37*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 98*x^7 + 8*x^6 + 26*x^5 + 116*x^4 + 45*x^3 + 8*x^2 + 13*x + 110, x^75 + 41*x^73 + 58*x^72 + 66*x^71 + 40*x^70 + 26*x^69 + 108*x^68 + 37*x^67 + 8*x^66 + 37*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 2*x^7 + 40*x^6 + 90*x^5 + 108*x^4 + 77*x^3 + 8*x^2 + 13*x + 10, x^75 + 41*x^73 + 30*x^72 + 50*x^71 + 120*x^70 + 106*x^69 + 4*x^68 + 53*x^67 + 88*x^66 + 85*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 114*x^7 + 120*x^6 + 42*x^5 + 4*x^4 + 93*x^3 + 88*x^2 + 61*x + 46, x^75 + 41*x^73 + 46*x^72 + 2*x^71 + 104*x^70 + 58*x^69 + 84*x^68 + 37*x^67 + 40*x^66 + 69*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 66*x^7 + 104*x^6 + 122*x^5 + 84*x^4 + 77*x^3 + 40*x^2 + 45*x + 14, x^75 + 41*x^73 + 50*x^72 + 114*x^71 + 104*x^70 + 106*x^69 + 60*x^68 + 117*x^67 + 72*x^66 + 85*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 50*x^7 + 104*x^6 + 42*x^5 + 60*x^4 + 29*x^3 + 72*x^2 + 61*x + 66, x^75 + 41*x^73 + 86*x^72 + 2*x^71 + 56*x^70 + 26*x^69 + 84*x^68 + 101*x^67 + 24*x^66 + 37*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 66*x^7 + 56*x^6 + 90*x^5 + 84*x^4 + 13*x^3 + 24*x^2 + 13*x + 38, x^75 + 41*x^73 + 10*x^72 + 66*x^71 + 40*x^70 + 26*x^69 + 12*x^68 + 37*x^67 + 8*x^66 + 37*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 2*x^7 + 40*x^6 + 90*x^5 + 12*x^4 + 77*x^3 + 8*x^2 + 13*x + 26, x^75 + 41*x^73 + 26*x^72 + 82*x^71 + 24*x^70 + 106*x^69 + 28*x^68 + 85*x^67 + 88*x^66 + 21*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 18*x^7 + 24*x^6 + 42*x^5 + 28*x^4 + 125*x^3 + 88*x^2 + 125*x + 58, x^75 + 41*x^73 + 66*x^72 + 34*x^71 + 88*x^70 + 26*x^69 + 12*x^68 + 5*x^67 + 24*x^66 + 101*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 98*x^7 + 88*x^6 + 90*x^5 + 12*x^4 + 45*x^3 + 24*x^2 + 77*x + 34, x^75 + 41*x^73 + 34*x^72 + 98*x^71 + 120*x^70 + 90*x^69 + 108*x^68 + 69*x^67 + 120*x^66 + 37*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 34*x^7 + 120*x^6 + 26*x^5 + 108*x^4 + 109*x^3 + 120*x^2 + 13*x + 98, x^75 + 41*x^73 + 82*x^72 + 114*x^71 + 72*x^70 + 42*x^69 + 28*x^68 + 117*x^67 + 104*x^66 + 21*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 50*x^7 + 72*x^6 + 106*x^5 + 28*x^4 + 29*x^3 + 104*x^2 + 125*x + 66, x^75 + 41*x^73 + 94*x^72 + 82*x^71 + 88*x^70 + 74*x^69 + 36*x^68 + 21*x^67 + 120*x^66 + 117*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 18*x^7 + 88*x^6 + 10*x^5 + 36*x^4 + 61*x^3 + 120*x^2 + 93*x + 78, x^75 + 41*x^73 + 82*x^72 + 34*x^71 + 24*x^70 + 90*x^69 + 44*x^68 + 5*x^67 + 88*x^66 + 37*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 98*x^7 + 24*x^6 + 26*x^5 + 44*x^4 + 45*x^3 + 88*x^2 + 13*x + 114, x^75 + 41*x^73 + 102*x^72 + 2*x^71 + 56*x^70 + 90*x^69 + 52*x^68 + 101*x^67 + 24*x^66 + 101*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 66*x^7 + 56*x^6 + 26*x^5 + 52*x^4 + 13*x^3 + 24*x^2 + 77*x + 54, x^75 + 41*x^73 + 50*x^72 + 34*x^71 + 56*x^70 + 26*x^69 + 76*x^68 + 5*x^67 + 56*x^66 + 101*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 98*x^7 + 56*x^6 + 90*x^5 + 76*x^4 + 45*x^3 + 56*x^2 + 77*x + 114, x^75 + 41*x^73 + 66*x^72 + 18*x^71 + 8*x^70 + 10*x^69 + 124*x^68 + 85*x^67 + 40*x^66 + 53*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 82*x^7 + 8*x^6 + 74*x^5 + 124*x^4 + 125*x^3 + 40*x^2 + 29*x + 114, x^75 + 41*x^73 + 14*x^72 + 18*x^71 + 120*x^70 + 10*x^69 + 36*x^68 + 85*x^67 + 88*x^66 + 53*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 82*x^7 + 120*x^6 + 74*x^5 + 36*x^4 + 125*x^3 + 88*x^2 + 29*x + 30, x^75 + 41*x^73 + 90*x^72 + 18*x^71 + 24*x^70 + 42*x^69 + 28*x^68 + 21*x^67 + 88*x^66 + 85*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 82*x^7 + 24*x^6 + 106*x^5 + 28*x^4 + 61*x^3 + 88*x^2 + 61*x + 122, x^75 + 41*x^73 + 118*x^72 + 66*x^71 + 56*x^70 + 26*x^69 + 84*x^68 + 37*x^67 + 24*x^66 + 37*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 2*x^7 + 56*x^6 + 90*x^5 + 84*x^4 + 77*x^3 + 24*x^2 + 13*x + 6, x^75 + 41*x^73 + 74*x^72 + 50*x^71 + 120*x^70 + 10*x^69 + 28*x^68 + 117*x^67 + 120*x^66 + 117*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 114*x^7 + 120*x^6 + 74*x^5 + 28*x^4 + 29*x^3 + 120*x^2 + 93*x + 10, x^75 + 41*x^73 + 50*x^72 + 2*x^71 + 120*x^70 + 58*x^69 + 76*x^68 + 37*x^67 + 120*x^66 + 69*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 66*x^7 + 120*x^6 + 122*x^5 + 76*x^4 + 77*x^3 + 120*x^2 + 45*x + 114, x^75 + 41*x^73 + 34*x^72 + 34*x^71 + 88*x^70 + 26*x^69 + 76*x^68 + 5*x^67 + 24*x^66 + 101*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 98*x^7 + 88*x^6 + 90*x^5 + 76*x^4 + 45*x^3 + 24*x^2 + 77*x + 2, x^75 + 41*x^73 + 74*x^72 + 98*x^71 + 72*x^70 + 58*x^69 + 44*x^68 + 5*x^67 + 104*x^66 + 5*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 34*x^7 + 72*x^6 + 122*x^5 + 44*x^4 + 45*x^3 + 104*x^2 + 109*x + 58, x^75 + 41*x^73 + 110*x^72 + 50*x^71 + 56*x^70 + 106*x^69 + 100*x^68 + 53*x^67 + 24*x^66 + 85*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 114*x^7 + 56*x^6 + 42*x^5 + 100*x^4 + 93*x^3 + 24*x^2 + 61*x + 126, x^75 + 41*x^73 + 102*x^72 + 34*x^71 + 24*x^70 + 58*x^69 + 84*x^68 + 69*x^67 + 56*x^66 + 5*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 98*x^7 + 24*x^6 + 122*x^5 + 84*x^4 + 109*x^3 + 56*x^2 + 109*x + 22, x^75 + 41*x^73 + 66*x^72 + 98*x^71 + 56*x^70 + 90*x^69 + 108*x^68 + 69*x^67 + 56*x^66 + 37*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 34*x^7 + 56*x^6 + 26*x^5 + 108*x^4 + 109*x^3 + 56*x^2 + 13*x + 66, x^75 + 41*x^73 + 74*x^72 + 34*x^71 + 8*x^70 + 122*x^69 + 108*x^68 + 69*x^67 + 40*x^66 + 69*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 98*x^7 + 8*x^6 + 58*x^5 + 108*x^4 + 109*x^3 + 40*x^2 + 45*x + 122, x^75 + 41*x^73 + 18*x^72 + 34*x^71 + 120*x^70 + 90*x^69 + 12*x^68 + 5*x^67 + 120*x^66 + 37*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 98*x^7 + 120*x^6 + 26*x^5 + 12*x^4 + 45*x^3 + 120*x^2 + 13*x + 82, x^75 + 41*x^73 + 70*x^72 + 66*x^71 + 56*x^70 + 90*x^69 + 52*x^68 + 37*x^67 + 24*x^66 + 101*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 2*x^7 + 56*x^6 + 26*x^5 + 52*x^4 + 77*x^3 + 24*x^2 + 77*x + 86, x^75 + 41*x^73 + 78*x^72 + 2*x^71 + 72*x^70 + 58*x^69 + 116*x^68 + 37*x^67 + 72*x^66 + 69*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 66*x^7 + 72*x^6 + 122*x^5 + 116*x^4 + 77*x^3 + 72*x^2 + 45*x + 78, x^75 + 41*x^73 + 90*x^72 + 50*x^71 + 24*x^70 + 74*x^69 + 28*x^68 + 117*x^67 + 88*x^66 + 53*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 114*x^7 + 24*x^6 + 10*x^5 + 28*x^4 + 29*x^3 + 88*x^2 + 29*x + 122, x^75 + 41*x^73 + 126*x^72 + 2*x^71 + 104*x^70 + 58*x^69 + 116*x^68 + 37*x^67 + 40*x^66 + 69*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 66*x^7 + 104*x^6 + 122*x^5 + 116*x^4 + 77*x^3 + 40*x^2 + 45*x + 30, x^75 + 41*x^73 + 122*x^72 + 34*x^71 + 72*x^70 + 122*x^69 + 12*x^68 + 69*x^67 + 104*x^66 + 69*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 98*x^7 + 72*x^6 + 58*x^5 + 12*x^4 + 109*x^3 + 104*x^2 + 45*x + 42, x^75 + 41*x^73 + 102*x^72 + 82*x^71 + 72*x^70 + 42*x^69 + 4*x^68 + 85*x^67 + 72*x^66 + 85*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 18*x^7 + 72*x^6 + 106*x^5 + 4*x^4 + 125*x^3 + 72*x^2 + 61*x + 38, x^75 + 41*x^73 + 30*x^72 + 2*x^71 + 72*x^70 + 122*x^69 + 84*x^68 + 37*x^67 + 72*x^66 + 5*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 66*x^7 + 72*x^6 + 58*x^5 + 84*x^4 + 77*x^3 + 72*x^2 + 109*x + 30, x^75 + 41*x^73 + 74*x^72 + 114*x^71 + 88*x^70 + 74*x^69 + 124*x^68 + 53*x^67 + 24*x^66 + 53*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 50*x^7 + 88*x^6 + 10*x^5 + 124*x^4 + 93*x^3 + 24*x^2 + 29*x + 42, x^75 + 41*x^73 + 18*x^72 + 114*x^71 + 104*x^70 + 106*x^69 + 124*x^68 + 117*x^67 + 72*x^66 + 85*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 50*x^7 + 104*x^6 + 42*x^5 + 124*x^4 + 29*x^3 + 72*x^2 + 61*x + 34, x^75 + 41*x^73 + 14*x^72 + 2*x^71 + 40*x^70 + 122*x^69 + 20*x^68 + 37*x^67 + 104*x^66 + 5*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 66*x^7 + 40*x^6 + 58*x^5 + 20*x^4 + 77*x^3 + 104*x^2 + 109*x + 110, x^75 + 41*x^73 + 38*x^72 + 114*x^71 + 8*x^70 + 74*x^69 + 68*x^68 + 53*x^67 + 8*x^66 + 53*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 50*x^7 + 8*x^6 + 10*x^5 + 68*x^4 + 93*x^3 + 8*x^2 + 29*x + 38, x^75 + 41*x^73 + 70*x^72 + 82*x^71 + 104*x^70 + 106*x^69 + 36*x^68 + 85*x^67 + 40*x^66 + 21*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 18*x^7 + 104*x^6 + 42*x^5 + 36*x^4 + 125*x^3 + 40*x^2 + 125*x + 38, x^75 + 41*x^73 + 82*x^72 + 66*x^71 + 56*x^70 + 122*x^69 + 76*x^68 + 101*x^67 + 56*x^66 + 5*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 2*x^7 + 56*x^6 + 58*x^5 + 76*x^4 + 13*x^3 + 56*x^2 + 109*x + 82, x^75 + 41*x^73 + 70*x^72 + 66*x^71 + 88*x^70 + 90*x^69 + 84*x^68 + 37*x^67 + 120*x^66 + 101*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 2*x^7 + 88*x^6 + 26*x^5 + 84*x^4 + 77*x^3 + 120*x^2 + 77*x + 54, x^75 + 41*x^73 + 58*x^72 + 18*x^71 + 24*x^70 + 106*x^69 + 28*x^68 + 21*x^67 + 88*x^66 + 21*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 82*x^7 + 24*x^6 + 42*x^5 + 28*x^4 + 61*x^3 + 88*x^2 + 125*x + 26, x^75 + 41*x^73 + 46*x^72 + 18*x^71 + 24*x^70 + 10*x^69 + 4*x^68 + 85*x^67 + 56*x^66 + 53*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 82*x^7 + 24*x^6 + 74*x^5 + 4*x^4 + 125*x^3 + 56*x^2 + 29*x + 30, x^75 + 41*x^73 + 78*x^72 + 34*x^71 + 8*x^70 + 90*x^69 + 52*x^68 + 5*x^67 + 8*x^66 + 37*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 98*x^7 + 8*x^6 + 26*x^5 + 52*x^4 + 45*x^3 + 8*x^2 + 13*x + 14, x^75 + 41*x^73 + 110*x^72 + 50*x^71 + 24*x^70 + 42*x^69 + 4*x^68 + 53*x^67 + 56*x^66 + 21*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 114*x^7 + 24*x^6 + 106*x^5 + 4*x^4 + 93*x^3 + 56*x^2 + 125*x + 94, x^75 + 41*x^73 + 26*x^72 + 98*x^71 + 72*x^70 + 122*x^69 + 12*x^68 + 5*x^67 + 104*x^66 + 69*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 34*x^7 + 72*x^6 + 58*x^5 + 12*x^4 + 45*x^3 + 104*x^2 + 45*x + 10, x^75 + 41*x^73 + 6*x^72 + 50*x^71 + 104*x^70 + 10*x^69 + 100*x^68 + 117*x^67 + 40*x^66 + 117*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 114*x^7 + 104*x^6 + 74*x^5 + 100*x^4 + 29*x^3 + 40*x^2 + 93*x + 38, x^75 + 41*x^73 + 110*x^72 + 50*x^71 + 88*x^70 + 106*x^69 + 4*x^68 + 53*x^67 + 120*x^66 + 85*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 114*x^7 + 88*x^6 + 42*x^5 + 4*x^4 + 93*x^3 + 120*x^2 + 61*x + 94, x^75 + 41*x^73 + 118*x^72 + 114*x^71 + 104*x^70 + 74*x^69 + 68*x^68 + 53*x^67 + 40*x^66 + 53*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 50*x^7 + 104*x^6 + 10*x^5 + 68*x^4 + 93*x^3 + 40*x^2 + 29*x + 86, x^75 + 41*x^73 + 74*x^72 + 34*x^71 + 40*x^70 + 122*x^69 + 12*x^68 + 69*x^67 + 8*x^66 + 69*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 98*x^7 + 40*x^6 + 58*x^5 + 12*x^4 + 109*x^3 + 8*x^2 + 45*x + 90, x^75 + 41*x^73 + 106*x^72 + 50*x^71 + 56*x^70 + 10*x^69 + 28*x^68 + 117*x^67 + 56*x^66 + 117*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 114*x^7 + 56*x^6 + 74*x^5 + 28*x^4 + 29*x^3 + 56*x^2 + 93*x + 106, x^75 + 41*x^73 + 82*x^72 + 2*x^71 + 24*x^70 + 58*x^69 + 44*x^68 + 37*x^67 + 88*x^66 + 69*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 66*x^7 + 24*x^6 + 122*x^5 + 44*x^4 + 77*x^3 + 88*x^2 + 45*x + 114, x^75 + 41*x^73 + 30*x^72 + 66*x^71 + 104*x^70 + 58*x^69 + 116*x^68 + 101*x^67 + 40*x^66 + 69*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 2*x^7 + 104*x^6 + 122*x^5 + 116*x^4 + 13*x^3 + 40*x^2 + 45*x + 126, x^75 + 41*x^73 + 110*x^72 + 82*x^71 + 24*x^70 + 10*x^69 + 68*x^68 + 21*x^67 + 56*x^66 + 53*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 18*x^7 + 24*x^6 + 74*x^5 + 68*x^4 + 61*x^3 + 56*x^2 + 29*x + 30, x^75 + 41*x^73 + 46*x^72 + 66*x^71 + 72*x^70 + 58*x^69 + 116*x^68 + 101*x^67 + 72*x^66 + 69*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 2*x^7 + 72*x^6 + 122*x^5 + 116*x^4 + 13*x^3 + 72*x^2 + 45*x + 110, x^75 + 41*x^73 + 94*x^72 + 34*x^71 + 104*x^70 + 26*x^69 + 116*x^68 + 5*x^67 + 40*x^66 + 101*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 98*x^7 + 104*x^6 + 90*x^5 + 116*x^4 + 45*x^3 + 40*x^2 + 77*x + 62, x^75 + 41*x^73 + 66*x^72 + 82*x^71 + 40*x^70 + 74*x^69 + 28*x^68 + 21*x^67 + 8*x^66 + 117*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 18*x^7 + 40*x^6 + 10*x^5 + 28*x^4 + 61*x^3 + 8*x^2 + 93*x + 82, x^75 + 41*x^73 + 18*x^72 + 2*x^71 + 88*x^70 + 58*x^69 + 108*x^68 + 37*x^67 + 24*x^66 + 69*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 66*x^7 + 88*x^6 + 122*x^5 + 108*x^4 + 77*x^3 + 24*x^2 + 45*x + 114, x^75 + 41*x^73 + 38*x^72 + 34*x^71 + 56*x^70 + 58*x^69 + 116*x^68 + 69*x^67 + 24*x^66 + 5*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 98*x^7 + 56*x^6 + 122*x^5 + 116*x^4 + 109*x^3 + 24*x^2 + 109*x + 54, x^75 + 41*x^73 + 2*x^72 + 98*x^71 + 120*x^70 + 90*x^69 + 44*x^68 + 69*x^67 + 120*x^66 + 37*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 34*x^7 + 120*x^6 + 26*x^5 + 44*x^4 + 109*x^3 + 120*x^2 + 13*x + 66, x^75 + 41*x^73 + 90*x^72 + 114*x^71 + 88*x^70 + 74*x^69 + 28*x^68 + 53*x^67 + 24*x^66 + 53*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 50*x^7 + 88*x^6 + 10*x^5 + 28*x^4 + 93*x^3 + 24*x^2 + 29*x + 122, x^75 + 41*x^73 + 106*x^72 + 18*x^71 + 56*x^70 + 106*x^69 + 28*x^68 + 21*x^67 + 56*x^66 + 21*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 82*x^7 + 56*x^6 + 42*x^5 + 28*x^4 + 61*x^3 + 56*x^2 + 125*x + 106, x^75 + 41*x^73 + 50*x^72 + 66*x^71 + 88*x^70 + 122*x^69 + 44*x^68 + 101*x^67 + 24*x^66 + 5*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 2*x^7 + 88*x^6 + 58*x^5 + 44*x^4 + 13*x^3 + 24*x^2 + 109*x + 18, x^75 + 41*x^73 + 54*x^72 + 98*x^71 + 88*x^70 + 58*x^69 + 116*x^68 + 5*x^67 + 120*x^66 + 5*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 34*x^7 + 88*x^6 + 122*x^5 + 116*x^4 + 45*x^3 + 120*x^2 + 109*x + 38, x^75 + 41*x^73 + 126*x^72 + 82*x^71 + 24*x^70 + 74*x^69 + 36*x^68 + 21*x^67 + 56*x^66 + 117*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 18*x^7 + 24*x^6 + 10*x^5 + 36*x^4 + 61*x^3 + 56*x^2 + 93*x + 46, x^75 + 41*x^73 + 86*x^72 + 98*x^71 + 56*x^70 + 122*x^69 + 84*x^68 + 5*x^67 + 24*x^66 + 69*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 34*x^7 + 56*x^6 + 58*x^5 + 84*x^4 + 45*x^3 + 24*x^2 + 45*x + 38, x^75 + 41*x^73 + 122*x^72 + 98*x^71 + 40*x^70 + 122*x^69 + 44*x^68 + 5*x^67 + 8*x^66 + 69*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 34*x^7 + 40*x^6 + 58*x^5 + 44*x^4 + 45*x^3 + 8*x^2 + 45*x + 10, x^75 + 41*x^73 + 86*x^72 + 2*x^71 + 120*x^70 + 90*x^69 + 84*x^68 + 101*x^67 + 88*x^66 + 101*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 66*x^7 + 120*x^6 + 26*x^5 + 84*x^4 + 13*x^3 + 88*x^2 + 77*x + 38, x^75 + 41*x^73 + 26*x^72 + 66*x^71 + 72*x^70 + 26*x^69 + 76*x^68 + 37*x^67 + 104*x^66 + 37*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 2*x^7 + 72*x^6 + 90*x^5 + 76*x^4 + 77*x^3 + 104*x^2 + 13*x + 74, x^75 + 41*x^73 + 6*x^72 + 114*x^71 + 8*x^70 + 10*x^69 + 68*x^68 + 53*x^67 + 8*x^66 + 117*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 50*x^7 + 8*x^6 + 74*x^5 + 68*x^4 + 93*x^3 + 8*x^2 + 93*x + 70, x^75 + 41*x^73 + 18*x^72 + 82*x^71 + 104*x^70 + 10*x^69 + 60*x^68 + 21*x^67 + 72*x^66 + 53*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 18*x^7 + 104*x^6 + 74*x^5 + 60*x^4 + 61*x^3 + 72*x^2 + 29*x + 98, x^75 + 41*x^73 + 118*x^72 + 82*x^71 + 40*x^70 + 42*x^69 + 4*x^68 + 85*x^67 + 104*x^66 + 85*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 18*x^7 + 40*x^6 + 106*x^5 + 4*x^4 + 125*x^3 + 104*x^2 + 61*x + 22, x^75 + 41*x^73 + 2*x^72 + 34*x^71 + 24*x^70 + 26*x^69 + 76*x^68 + 5*x^67 + 88*x^66 + 101*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 98*x^7 + 24*x^6 + 90*x^5 + 76*x^4 + 45*x^3 + 88*x^2 + 77*x + 34, x^75 + 41*x^73 + 86*x^72 + 18*x^71 + 104*x^70 + 106*x^69 + 4*x^68 + 21*x^67 + 40*x^66 + 21*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 82*x^7 + 104*x^6 + 42*x^5 + 4*x^4 + 61*x^3 + 40*x^2 + 125*x + 54, x^75 + 41*x^73 + 102*x^72 + 50*x^71 + 104*x^70 + 10*x^69 + 36*x^68 + 117*x^67 + 40*x^66 + 117*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 114*x^7 + 104*x^6 + 74*x^5 + 36*x^4 + 29*x^3 + 40*x^2 + 93*x + 6, x^75 + 41*x^73 + 114*x^72 + 34*x^71 + 88*x^70 + 26*x^69 + 108*x^68 + 5*x^67 + 24*x^66 + 101*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 98*x^7 + 88*x^6 + 90*x^5 + 108*x^4 + 45*x^3 + 24*x^2 + 77*x + 18, x^75 + 41*x^73 + 106*x^72 + 66*x^71 + 72*x^70 + 26*x^69 + 108*x^68 + 37*x^67 + 104*x^66 + 37*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 2*x^7 + 72*x^6 + 90*x^5 + 108*x^4 + 77*x^3 + 104*x^2 + 13*x + 90, x^75 + 41*x^73 + 114*x^72 + 34*x^71 + 120*x^70 + 26*x^69 + 12*x^68 + 5*x^67 + 120*x^66 + 101*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 98*x^7 + 120*x^6 + 90*x^5 + 12*x^4 + 45*x^3 + 120*x^2 + 77*x + 114, x^75 + 41*x^73 + 86*x^72 + 18*x^71 + 40*x^70 + 106*x^69 + 68*x^68 + 21*x^67 + 104*x^66 + 21*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 82*x^7 + 40*x^6 + 42*x^5 + 68*x^4 + 61*x^3 + 104*x^2 + 125*x + 118, x^75 + 41*x^73 + 6*x^72 + 114*x^71 + 72*x^70 + 10*x^69 + 4*x^68 + 53*x^67 + 72*x^66 + 117*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 50*x^7 + 72*x^6 + 74*x^5 + 4*x^4 + 93*x^3 + 72*x^2 + 93*x + 6, x^75 + 41*x^73 + 34*x^72 + 82*x^71 + 8*x^70 + 74*x^69 + 60*x^68 + 21*x^67 + 40*x^66 + 117*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 18*x^7 + 8*x^6 + 10*x^5 + 60*x^4 + 61*x^3 + 40*x^2 + 93*x + 82, x^75 + 41*x^73 + 106*x^72 + 66*x^71 + 104*x^70 + 26*x^69 + 12*x^68 + 37*x^67 + 72*x^66 + 37*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 2*x^7 + 104*x^6 + 90*x^5 + 12*x^4 + 77*x^3 + 72*x^2 + 13*x + 58, x^75 + 41*x^73 + 114*x^72 + 66*x^71 + 56*x^70 + 122*x^69 + 12*x^68 + 101*x^67 + 56*x^66 + 5*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 2*x^7 + 56*x^6 + 58*x^5 + 12*x^4 + 13*x^3 + 56*x^2 + 109*x + 114, x^75 + 41*x^73 + 70*x^72 + 2*x^71 + 88*x^70 + 90*x^69 + 20*x^68 + 101*x^67 + 120*x^66 + 101*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 66*x^7 + 88*x^6 + 26*x^5 + 20*x^4 + 13*x^3 + 120*x^2 + 77*x + 118, x^75 + 41*x^73 + 6*x^72 + 114*x^71 + 72*x^70 + 74*x^69 + 68*x^68 + 53*x^67 + 72*x^66 + 53*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 50*x^7 + 72*x^6 + 10*x^5 + 68*x^4 + 93*x^3 + 72*x^2 + 29*x + 70, x^75 + 41*x^73 + 22*x^72 + 18*x^71 + 8*x^70 + 106*x^69 + 36*x^68 + 21*x^67 + 8*x^66 + 21*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 82*x^7 + 8*x^6 + 42*x^5 + 36*x^4 + 61*x^3 + 8*x^2 + 125*x + 86, x^75 + 41*x^73 + 102*x^72 + 18*x^71 + 40*x^70 + 42*x^69 + 36*x^68 + 21*x^67 + 104*x^66 + 85*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 82*x^7 + 40*x^6 + 106*x^5 + 36*x^4 + 61*x^3 + 104*x^2 + 61*x + 6, x^75 + 41*x^73 + 6*x^72 + 66*x^71 + 24*x^70 + 26*x^69 + 84*x^68 + 37*x^67 + 56*x^66 + 37*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 2*x^7 + 24*x^6 + 90*x^5 + 84*x^4 + 77*x^3 + 56*x^2 + 13*x + 118, x^75 + 41*x^73 + 6*x^72 + 18*x^71 + 104*x^70 + 42*x^69 + 36*x^68 + 21*x^67 + 40*x^66 + 85*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 82*x^7 + 104*x^6 + 106*x^5 + 36*x^4 + 61*x^3 + 40*x^2 + 61*x + 102, x^75 + 41*x^73 + 34*x^72 + 2*x^71 + 24*x^70 + 122*x^69 + 12*x^68 + 37*x^67 + 88*x^66 + 5*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 66*x^7 + 24*x^6 + 58*x^5 + 12*x^4 + 77*x^3 + 88*x^2 + 109*x + 66, x^75 + 41*x^73 + 74*x^72 + 114*x^71 + 56*x^70 + 10*x^69 + 28*x^68 + 53*x^67 + 56*x^66 + 117*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 50*x^7 + 56*x^6 + 74*x^5 + 28*x^4 + 93*x^3 + 56*x^2 + 93*x + 10, x^75 + 41*x^73 + 94*x^72 + 66*x^71 + 104*x^70 + 58*x^69 + 116*x^68 + 101*x^67 + 40*x^66 + 69*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 2*x^7 + 104*x^6 + 122*x^5 + 116*x^4 + 13*x^3 + 40*x^2 + 45*x + 62, x^75 + 41*x^73 + 90*x^72 + 98*x^71 + 104*x^70 + 122*x^69 + 44*x^68 + 5*x^67 + 72*x^66 + 69*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 34*x^7 + 104*x^6 + 58*x^5 + 44*x^4 + 45*x^3 + 72*x^2 + 45*x + 42, x^75 + 41*x^73 + 94*x^72 + 98*x^71 + 40*x^70 + 90*x^69 + 52*x^68 + 69*x^67 + 104*x^66 + 37*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 34*x^7 + 40*x^6 + 26*x^5 + 52*x^4 + 109*x^3 + 104*x^2 + 13*x + 126, x^75 + 41*x^73 + 106*x^72 + 2*x^71 + 40*x^70 + 90*x^69 + 76*x^68 + 101*x^67 + 8*x^66 + 101*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 66*x^7 + 40*x^6 + 26*x^5 + 76*x^4 + 13*x^3 + 8*x^2 + 77*x + 122, x^75 + 41*x^73 + 58*x^72 + 82*x^71 + 24*x^70 + 106*x^69 + 92*x^68 + 85*x^67 + 88*x^66 + 21*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 18*x^7 + 24*x^6 + 42*x^5 + 92*x^4 + 125*x^3 + 88*x^2 + 125*x + 90, x^75 + 41*x^73 + 6*x^72 + 82*x^71 + 8*x^70 + 42*x^69 + 4*x^68 + 85*x^67 + 8*x^66 + 85*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 18*x^7 + 8*x^6 + 106*x^5 + 4*x^4 + 125*x^3 + 8*x^2 + 61*x + 6, x^75 + 41*x^73 + 2*x^72 + 50*x^71 + 40*x^70 + 106*x^69 + 92*x^68 + 53*x^67 + 8*x^66 + 85*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 114*x^7 + 40*x^6 + 42*x^5 + 92*x^4 + 93*x^3 + 8*x^2 + 61*x + 82, x^75 + 41*x^73 + 46*x^72 + 2*x^71 + 72*x^70 + 122*x^69 + 116*x^68 + 37*x^67 + 72*x^66 + 5*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 66*x^7 + 72*x^6 + 58*x^5 + 116*x^4 + 77*x^3 + 72*x^2 + 109*x + 110, x^75 + 41*x^73 + 106*x^72 + 82*x^71 + 56*x^70 + 106*x^69 + 92*x^68 + 85*x^67 + 56*x^66 + 21*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 18*x^7 + 56*x^6 + 42*x^5 + 92*x^4 + 125*x^3 + 56*x^2 + 125*x + 42, x^75 + 41*x^73 + 78*x^72 + 66*x^71 + 8*x^70 + 58*x^69 + 116*x^68 + 101*x^67 + 8*x^66 + 69*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 2*x^7 + 8*x^6 + 122*x^5 + 116*x^4 + 13*x^3 + 8*x^2 + 45*x + 78, x^75 + 41*x^73 + 10*x^72 + 98*x^71 + 72*x^70 + 58*x^69 + 44*x^68 + 5*x^67 + 104*x^66 + 5*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 34*x^7 + 72*x^6 + 122*x^5 + 44*x^4 + 45*x^3 + 104*x^2 + 109*x + 122, x^75 + 41*x^73 + 46*x^72 + 34*x^71 + 104*x^70 + 90*x^69 + 84*x^68 + 5*x^67 + 40*x^66 + 37*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 98*x^7 + 104*x^6 + 26*x^5 + 84*x^4 + 45*x^3 + 40*x^2 + 13*x + 14, x^75 + 41*x^73 + 54*x^72 + 114*x^71 + 40*x^70 + 10*x^69 + 68*x^68 + 53*x^67 + 104*x^66 + 117*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 50*x^7 + 40*x^6 + 74*x^5 + 68*x^4 + 93*x^3 + 104*x^2 + 93*x + 22, x^75 + 41*x^73 + 122*x^72 + 82*x^71 + 56*x^70 + 106*x^69 + 124*x^68 + 85*x^67 + 56*x^66 + 21*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 18*x^7 + 56*x^6 + 42*x^5 + 124*x^4 + 125*x^3 + 56*x^2 + 125*x + 122, x^75 + 41*x^73 + 90*x^72 + 66*x^71 + 40*x^70 + 90*x^69 + 108*x^68 + 37*x^67 + 8*x^66 + 101*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 2*x^7 + 40*x^6 + 26*x^5 + 108*x^4 + 77*x^3 + 8*x^2 + 77*x + 106, x^75 + 41*x^73 + 38*x^72 + 50*x^71 + 8*x^70 + 10*x^69 + 68*x^68 + 117*x^67 + 8*x^66 + 117*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 114*x^7 + 8*x^6 + 74*x^5 + 68*x^4 + 29*x^3 + 8*x^2 + 93*x + 38, x^75 + 41*x^73 + 74*x^72 + 66*x^71 + 40*x^70 + 26*x^69 + 12*x^68 + 37*x^67 + 8*x^66 + 37*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 2*x^7 + 40*x^6 + 90*x^5 + 12*x^4 + 77*x^3 + 8*x^2 + 13*x + 90, x^75 + 41*x^73 + 66*x^72 + 2*x^71 + 88*x^70 + 58*x^69 + 76*x^68 + 37*x^67 + 24*x^66 + 69*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 66*x^7 + 88*x^6 + 122*x^5 + 76*x^4 + 77*x^3 + 24*x^2 + 45*x + 98, x^75 + 41*x^73 + 62*x^72 + 66*x^71 + 72*x^70 + 58*x^69 + 20*x^68 + 101*x^67 + 72*x^66 + 69*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 2*x^7 + 72*x^6 + 122*x^5 + 20*x^4 + 13*x^3 + 72*x^2 + 45*x + 62, x^75 + 41*x^73 + 126*x^72 + 18*x^71 + 120*x^70 + 10*x^69 + 4*x^68 + 85*x^67 + 88*x^66 + 53*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 82*x^7 + 120*x^6 + 74*x^5 + 4*x^4 + 125*x^3 + 88*x^2 + 29*x + 78, x^75 + 41*x^73 + 14*x^72 + 98*x^71 + 104*x^70 + 90*x^69 + 84*x^68 + 69*x^67 + 40*x^66 + 37*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 34*x^7 + 104*x^6 + 26*x^5 + 84*x^4 + 109*x^3 + 40*x^2 + 13*x + 46, x^75 + 41*x^73 + 114*x^72 + 98*x^71 + 24*x^70 + 90*x^69 + 44*x^68 + 69*x^67 + 88*x^66 + 37*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 34*x^7 + 24*x^6 + 26*x^5 + 44*x^4 + 109*x^3 + 88*x^2 + 13*x + 82, x^75 + 41*x^73 + 118*x^72 + 114*x^71 + 72*x^70 + 74*x^69 + 36*x^68 + 53*x^67 + 72*x^66 + 53*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 50*x^7 + 72*x^6 + 10*x^5 + 36*x^4 + 93*x^3 + 72*x^2 + 29*x + 118, x^75 + 41*x^73 + 58*x^72 + 98*x^71 + 104*x^70 + 122*x^69 + 108*x^68 + 5*x^67 + 72*x^66 + 69*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 34*x^7 + 104*x^6 + 58*x^5 + 108*x^4 + 45*x^3 + 72*x^2 + 45*x + 10, x^75 + 41*x^73 + 98*x^72 + 18*x^71 + 104*x^70 + 10*x^69 + 28*x^68 + 85*x^67 + 72*x^66 + 53*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 82*x^7 + 104*x^6 + 74*x^5 + 28*x^4 + 125*x^3 + 72*x^2 + 29*x + 50, x^75 + 41*x^73 + 14*x^72 + 34*x^71 + 8*x^70 + 26*x^69 + 116*x^68 + 5*x^67 + 8*x^66 + 101*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 98*x^7 + 8*x^6 + 90*x^5 + 116*x^4 + 45*x^3 + 8*x^2 + 77*x + 14, x^75 + 41*x^73 + 102*x^72 + 34*x^71 + 120*x^70 + 58*x^69 + 52*x^68 + 69*x^67 + 88*x^66 + 5*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 98*x^7 + 120*x^6 + 122*x^5 + 52*x^4 + 109*x^3 + 88*x^2 + 109*x + 54, x^75 + 41*x^73 + 86*x^72 + 34*x^71 + 120*x^70 + 122*x^69 + 84*x^68 + 69*x^67 + 88*x^66 + 69*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 98*x^7 + 120*x^6 + 58*x^5 + 84*x^4 + 109*x^3 + 88*x^2 + 45*x + 38, x^75 + 41*x^73 + 74*x^72 + 34*x^71 + 40*x^70 + 58*x^69 + 76*x^68 + 69*x^67 + 8*x^66 + 5*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 98*x^7 + 40*x^6 + 122*x^5 + 76*x^4 + 109*x^3 + 8*x^2 + 109*x + 26, x^75 + 41*x^73 + 10*x^72 + 50*x^71 + 56*x^70 + 74*x^69 + 28*x^68 + 117*x^67 + 56*x^66 + 53*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 114*x^7 + 56*x^6 + 10*x^5 + 28*x^4 + 29*x^3 + 56*x^2 + 29*x + 74, x^75 + 41*x^73 + 118*x^72 + 82*x^71 + 72*x^70 + 106*x^69 + 100*x^68 + 85*x^67 + 72*x^66 + 21*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 18*x^7 + 72*x^6 + 42*x^5 + 100*x^4 + 125*x^3 + 72*x^2 + 125*x + 54, x^75 + 41*x^73 + 70*x^72 + 18*x^71 + 72*x^70 + 42*x^69 + 4*x^68 + 21*x^67 + 72*x^66 + 85*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 82*x^7 + 72*x^6 + 106*x^5 + 4*x^4 + 61*x^3 + 72*x^2 + 61*x + 70, x^75 + 41*x^73 + 50*x^72 + 114*x^71 + 104*x^70 + 42*x^69 + 124*x^68 + 117*x^67 + 72*x^66 + 21*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 50*x^7 + 104*x^6 + 106*x^5 + 124*x^4 + 29*x^3 + 72*x^2 + 125*x + 2, x^75 + 41*x^73 + 18*x^72 + 34*x^71 + 24*x^70 + 90*x^69 + 44*x^68 + 5*x^67 + 88*x^66 + 37*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 98*x^7 + 24*x^6 + 26*x^5 + 44*x^4 + 45*x^3 + 88*x^2 + 13*x + 50, x^75 + 41*x^73 + 14*x^72 + 2*x^71 + 104*x^70 + 58*x^69 + 20*x^68 + 37*x^67 + 40*x^66 + 69*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 66*x^7 + 104*x^6 + 122*x^5 + 20*x^4 + 77*x^3 + 40*x^2 + 45*x + 110, x^75 + 41*x^73 + 14*x^72 + 18*x^71 + 24*x^70 + 10*x^69 + 68*x^68 + 85*x^67 + 56*x^66 + 53*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 82*x^7 + 24*x^6 + 74*x^5 + 68*x^4 + 125*x^3 + 56*x^2 + 29*x + 126, x^75 + 41*x^73 + 98*x^72 + 98*x^71 + 24*x^70 + 90*x^69 + 12*x^68 + 69*x^67 + 88*x^66 + 37*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 34*x^7 + 24*x^6 + 26*x^5 + 12*x^4 + 109*x^3 + 88*x^2 + 13*x + 2, x^75 + 41*x^73 + 66*x^72 + 66*x^71 + 56*x^70 + 58*x^69 + 108*x^68 + 101*x^67 + 56*x^66 + 69*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 2*x^7 + 56*x^6 + 122*x^5 + 108*x^4 + 13*x^3 + 56*x^2 + 45*x + 66, x^75 + 41*x^73 + 82*x^72 + 82*x^71 + 8*x^70 + 74*x^69 + 28*x^68 + 21*x^67 + 40*x^66 + 117*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 18*x^7 + 8*x^6 + 10*x^5 + 28*x^4 + 61*x^3 + 40*x^2 + 93*x + 66, x^75 + 41*x^73 + 126*x^72 + 66*x^71 + 72*x^70 + 122*x^69 + 84*x^68 + 101*x^67 + 72*x^66 + 5*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 2*x^7 + 72*x^6 + 58*x^5 + 84*x^4 + 13*x^3 + 72*x^2 + 109*x + 62, x^75 + 41*x^73 + 6*x^72 + 82*x^71 + 72*x^70 + 106*x^69 + 4*x^68 + 85*x^67 + 72*x^66 + 21*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 18*x^7 + 72*x^6 + 42*x^5 + 4*x^4 + 125*x^3 + 72*x^2 + 125*x + 6, x^75 + 41*x^73 + 102*x^72 + 66*x^71 + 120*x^70 + 26*x^69 + 116*x^68 + 37*x^67 + 88*x^66 + 37*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 2*x^7 + 120*x^6 + 90*x^5 + 116*x^4 + 77*x^3 + 88*x^2 + 13*x + 118, x^75 + 41*x^73 + 94*x^72 + 34*x^71 + 8*x^70 + 26*x^69 + 20*x^68 + 5*x^67 + 8*x^66 + 101*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 98*x^7 + 8*x^6 + 90*x^5 + 20*x^4 + 45*x^3 + 8*x^2 + 77*x + 30, x^75 + 41*x^73 + 118*x^72 + 50*x^71 + 40*x^70 + 74*x^69 + 68*x^68 + 117*x^67 + 104*x^66 + 53*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 114*x^7 + 40*x^6 + 10*x^5 + 68*x^4 + 29*x^3 + 104*x^2 + 29*x + 86, x^75 + 41*x^73 + 70*x^72 + 2*x^71 + 120*x^70 + 90*x^69 + 52*x^68 + 101*x^67 + 88*x^66 + 101*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 66*x^7 + 120*x^6 + 26*x^5 + 52*x^4 + 13*x^3 + 88*x^2 + 77*x + 86, x^75 + 41*x^73 + 38*x^72 + 98*x^71 + 24*x^70 + 58*x^69 + 20*x^68 + 5*x^67 + 56*x^66 + 5*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 34*x^7 + 24*x^6 + 122*x^5 + 20*x^4 + 45*x^3 + 56*x^2 + 109*x + 22, x^75 + 41*x^73 + 78*x^72 + 34*x^71 + 104*x^70 + 26*x^69 + 84*x^68 + 5*x^67 + 40*x^66 + 101*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 98*x^7 + 104*x^6 + 90*x^5 + 84*x^4 + 45*x^3 + 40*x^2 + 77*x + 110, x^75 + 41*x^73 + 50*x^72 + 114*x^71 + 40*x^70 + 42*x^69 + 60*x^68 + 117*x^67 + 8*x^66 + 21*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 50*x^7 + 40*x^6 + 106*x^5 + 60*x^4 + 29*x^3 + 8*x^2 + 125*x + 66, x^75 + 41*x^73 + 14*x^72 + 34*x^71 + 40*x^70 + 26*x^69 + 20*x^68 + 5*x^67 + 104*x^66 + 101*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 98*x^7 + 40*x^6 + 90*x^5 + 20*x^4 + 45*x^3 + 104*x^2 + 77*x + 110, x^75 + 41*x^73 + 26*x^72 + 2*x^71 + 8*x^70 + 90*x^69 + 12*x^68 + 101*x^67 + 40*x^66 + 101*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 66*x^7 + 8*x^6 + 26*x^5 + 12*x^4 + 13*x^3 + 40*x^2 + 77*x + 10, x^75 + 41*x^73 + 118*x^72 + 34*x^71 + 88*x^70 + 58*x^69 + 52*x^68 + 69*x^67 + 120*x^66 + 5*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 98*x^7 + 88*x^6 + 122*x^5 + 52*x^4 + 109*x^3 + 120*x^2 + 109*x + 38, x^75 + 41*x^73 + 70*x^72 + 34*x^71 + 24*x^70 + 58*x^69 + 20*x^68 + 69*x^67 + 56*x^66 + 5*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 98*x^7 + 24*x^6 + 122*x^5 + 20*x^4 + 109*x^3 + 56*x^2 + 109*x + 118, x^75 + 41*x^73 + 114*x^72 + 50*x^71 + 8*x^70 + 106*x^69 + 28*x^68 + 53*x^67 + 40*x^66 + 85*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 114*x^7 + 8*x^6 + 42*x^5 + 28*x^4 + 93*x^3 + 40*x^2 + 61*x + 34, x^75 + 41*x^73 + 26*x^72 + 50*x^71 + 88*x^70 + 10*x^69 + 28*x^68 + 117*x^67 + 24*x^66 + 117*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 114*x^7 + 88*x^6 + 74*x^5 + 28*x^4 + 29*x^3 + 24*x^2 + 93*x + 58, x^75 + 41*x^73 + 34*x^72 + 2*x^71 + 120*x^70 + 122*x^69 + 108*x^68 + 37*x^67 + 120*x^66 + 5*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 66*x^7 + 120*x^6 + 58*x^5 + 108*x^4 + 77*x^3 + 120*x^2 + 109*x + 98, x^75 + 41*x^73 + 62*x^72 + 34*x^71 + 72*x^70 + 90*x^69 + 84*x^68 + 5*x^67 + 72*x^66 + 37*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 98*x^7 + 72*x^6 + 26*x^5 + 84*x^4 + 45*x^3 + 72*x^2 + 13*x + 126, x^75 + 41*x^73 + 22*x^72 + 98*x^71 + 24*x^70 + 58*x^69 + 116*x^68 + 5*x^67 + 56*x^66 + 5*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 34*x^7 + 24*x^6 + 122*x^5 + 116*x^4 + 45*x^3 + 56*x^2 + 109*x + 70, x^75 + 41*x^73 + 70*x^72 + 82*x^71 + 72*x^70 + 106*x^69 + 4*x^68 + 85*x^67 + 72*x^66 + 21*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 18*x^7 + 72*x^6 + 42*x^5 + 4*x^4 + 125*x^3 + 72*x^2 + 125*x + 70, x^75 + 41*x^73 + 114*x^72 + 2*x^71 + 56*x^70 + 122*x^69 + 76*x^68 + 37*x^67 + 56*x^66 + 5*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 66*x^7 + 56*x^6 + 58*x^5 + 76*x^4 + 77*x^3 + 56*x^2 + 109*x + 50, x^75 + 41*x^73 + 90*x^72 + 114*x^71 + 120*x^70 + 74*x^69 + 60*x^68 + 53*x^67 + 120*x^66 + 53*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 50*x^7 + 120*x^6 + 10*x^5 + 60*x^4 + 93*x^3 + 120*x^2 + 29*x + 90, x^75 + 41*x^73 + 82*x^72 + 2*x^71 + 120*x^70 + 58*x^69 + 12*x^68 + 37*x^67 + 120*x^66 + 69*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 66*x^7 + 120*x^6 + 122*x^5 + 12*x^4 + 77*x^3 + 120*x^2 + 45*x + 18, x^75 + 41*x^73 + 38*x^72 + 18*x^71 + 8*x^70 + 42*x^69 + 4*x^68 + 21*x^67 + 8*x^66 + 85*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 82*x^7 + 8*x^6 + 106*x^5 + 4*x^4 + 61*x^3 + 8*x^2 + 61*x + 102, x^75 + 41*x^73 + 18*x^72 + 82*x^71 + 104*x^70 + 74*x^69 + 124*x^68 + 21*x^67 + 72*x^66 + 117*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 18*x^7 + 104*x^6 + 10*x^5 + 124*x^4 + 61*x^3 + 72*x^2 + 93*x + 34, x^75 + 41*x^73 + 2*x^72 + 18*x^71 + 8*x^70 + 10*x^69 + 124*x^68 + 85*x^67 + 40*x^66 + 53*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 82*x^7 + 8*x^6 + 74*x^5 + 124*x^4 + 125*x^3 + 40*x^2 + 29*x + 50, x^75 + 41*x^73 + 118*x^72 + 114*x^71 + 8*x^70 + 74*x^69 + 100*x^68 + 53*x^67 + 8*x^66 + 53*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 50*x^7 + 8*x^6 + 10*x^5 + 100*x^4 + 93*x^3 + 8*x^2 + 29*x + 54, x^75 + 41*x^73 + 6*x^72 + 34*x^71 + 120*x^70 + 122*x^69 + 52*x^68 + 69*x^67 + 88*x^66 + 69*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 98*x^7 + 120*x^6 + 58*x^5 + 52*x^4 + 109*x^3 + 88*x^2 + 45*x + 22, x^75 + 41*x^73 + 22*x^72 + 34*x^71 + 88*x^70 + 58*x^69 + 116*x^68 + 69*x^67 + 120*x^66 + 5*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 98*x^7 + 88*x^6 + 122*x^5 + 116*x^4 + 109*x^3 + 120*x^2 + 109*x + 70, x^75 + 41*x^73 + 26*x^72 + 82*x^71 + 120*x^70 + 106*x^69 + 124*x^68 + 85*x^67 + 120*x^66 + 21*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 18*x^7 + 120*x^6 + 42*x^5 + 124*x^4 + 125*x^3 + 120*x^2 + 125*x + 90, x^75 + 41*x^73 + 90*x^72 + 98*x^71 + 8*x^70 + 58*x^69 + 12*x^68 + 5*x^67 + 40*x^66 + 5*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 34*x^7 + 8*x^6 + 122*x^5 + 12*x^4 + 45*x^3 + 40*x^2 + 109*x + 74, x^75 + 41*x^73 + 38*x^72 + 114*x^71 + 104*x^70 + 10*x^69 + 100*x^68 + 53*x^67 + 40*x^66 + 117*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 50*x^7 + 104*x^6 + 74*x^5 + 100*x^4 + 93*x^3 + 40*x^2 + 93*x + 6, x^75 + 41*x^73 + 46*x^72 + 50*x^71 + 88*x^70 + 106*x^69 + 4*x^68 + 53*x^67 + 120*x^66 + 85*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 114*x^7 + 88*x^6 + 42*x^5 + 4*x^4 + 93*x^3 + 120*x^2 + 61*x + 30, x^75 + 41*x^73 + 74*x^72 + 18*x^71 + 88*x^70 + 106*x^69 + 124*x^68 + 21*x^67 + 24*x^66 + 21*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 82*x^7 + 88*x^6 + 42*x^5 + 124*x^4 + 61*x^3 + 24*x^2 + 125*x + 42, x^75 + 41*x^73 + 126*x^72 + 66*x^71 + 8*x^70 + 58*x^69 + 84*x^68 + 101*x^67 + 8*x^66 + 69*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 2*x^7 + 8*x^6 + 122*x^5 + 84*x^4 + 13*x^3 + 8*x^2 + 45*x + 62, x^75 + 41*x^73 + 58*x^72 + 18*x^71 + 120*x^70 + 42*x^69 + 60*x^68 + 21*x^67 + 120*x^66 + 85*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 82*x^7 + 120*x^6 + 106*x^5 + 60*x^4 + 61*x^3 + 120*x^2 + 61*x + 122, x^75 + 41*x^73 + 66*x^72 + 66*x^71 + 24*x^70 + 122*x^69 + 12*x^68 + 101*x^67 + 88*x^66 + 5*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 2*x^7 + 24*x^6 + 58*x^5 + 12*x^4 + 13*x^3 + 88*x^2 + 109*x + 34, x^75 + 41*x^73 + 66*x^72 + 2*x^71 + 56*x^70 + 122*x^69 + 108*x^68 + 37*x^67 + 56*x^66 + 5*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 66*x^7 + 56*x^6 + 58*x^5 + 108*x^4 + 77*x^3 + 56*x^2 + 109*x + 66, x^75 + 41*x^73 + 38*x^72 + 18*x^71 + 8*x^70 + 106*x^69 + 68*x^68 + 21*x^67 + 8*x^66 + 21*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 82*x^7 + 8*x^6 + 42*x^5 + 68*x^4 + 61*x^3 + 8*x^2 + 125*x + 38, x^75 + 41*x^73 + 46*x^72 + 114*x^71 + 56*x^70 + 42*x^69 + 100*x^68 + 117*x^67 + 24*x^66 + 21*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 50*x^7 + 56*x^6 + 106*x^5 + 100*x^4 + 29*x^3 + 24*x^2 + 125*x + 62, x^75 + 41*x^73 + 6*x^72 + 34*x^71 + 88*x^70 + 122*x^69 + 20*x^68 + 69*x^67 + 120*x^66 + 69*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 98*x^7 + 88*x^6 + 58*x^5 + 20*x^4 + 109*x^3 + 120*x^2 + 45*x + 54, x^75 + 41*x^73 + 30*x^72 + 34*x^71 + 8*x^70 + 90*x^69 + 84*x^68 + 5*x^67 + 8*x^66 + 37*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 98*x^7 + 8*x^6 + 26*x^5 + 84*x^4 + 45*x^3 + 8*x^2 + 13*x + 30, x^75 + 41*x^73 + 50*x^72 + 2*x^71 + 24*x^70 + 58*x^69 + 108*x^68 + 37*x^67 + 88*x^66 + 69*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 66*x^7 + 24*x^6 + 122*x^5 + 108*x^4 + 77*x^3 + 88*x^2 + 45*x + 82, x^75 + 41*x^73 + 46*x^72 + 114*x^71 + 120*x^70 + 106*x^69 + 100*x^68 + 117*x^67 + 88*x^66 + 85*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 50*x^7 + 120*x^6 + 42*x^5 + 100*x^4 + 29*x^3 + 88*x^2 + 61*x + 62, x^75 + 41*x^73 + 54*x^72 + 66*x^71 + 24*x^70 + 26*x^69 + 52*x^68 + 37*x^67 + 56*x^66 + 37*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 2*x^7 + 24*x^6 + 90*x^5 + 52*x^4 + 77*x^3 + 56*x^2 + 13*x + 102, x^75 + 41*x^73 + 54*x^72 + 2*x^71 + 56*x^70 + 90*x^69 + 84*x^68 + 101*x^67 + 24*x^66 + 101*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 66*x^7 + 56*x^6 + 26*x^5 + 84*x^4 + 13*x^3 + 24*x^2 + 77*x + 70, x^75 + 41*x^73 + 10*x^72 + 50*x^71 + 88*x^70 + 74*x^69 + 60*x^68 + 117*x^67 + 24*x^66 + 53*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 114*x^7 + 88*x^6 + 10*x^5 + 60*x^4 + 29*x^3 + 24*x^2 + 29*x + 42, x^75 + 41*x^73 + 118*x^72 + 2*x^71 + 88*x^70 + 90*x^69 + 116*x^68 + 101*x^67 + 120*x^66 + 101*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 66*x^7 + 88*x^6 + 26*x^5 + 116*x^4 + 13*x^3 + 120*x^2 + 77*x + 102, x^75 + 41*x^73 + 86*x^72 + 50*x^71 + 40*x^70 + 74*x^69 + 4*x^68 + 117*x^67 + 104*x^66 + 53*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 114*x^7 + 40*x^6 + 10*x^5 + 4*x^4 + 29*x^3 + 104*x^2 + 29*x + 54, x^75 + 41*x^73 + 106*x^72 + 18*x^71 + 120*x^70 + 106*x^69 + 92*x^68 + 21*x^67 + 120*x^66 + 21*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 82*x^7 + 120*x^6 + 42*x^5 + 92*x^4 + 61*x^3 + 120*x^2 + 125*x + 42, x^75 + 41*x^73 + 118*x^72 + 18*x^71 + 104*x^70 + 106*x^69 + 68*x^68 + 21*x^67 + 40*x^66 + 21*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 82*x^7 + 104*x^6 + 42*x^5 + 68*x^4 + 61*x^3 + 40*x^2 + 125*x + 86, x^75 + 41*x^73 + 66*x^72 + 2*x^71 + 88*x^70 + 122*x^69 + 12*x^68 + 37*x^67 + 24*x^66 + 5*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 66*x^7 + 88*x^6 + 58*x^5 + 12*x^4 + 77*x^3 + 24*x^2 + 109*x + 34, x^75 + 41*x^73 + 122*x^72 + 18*x^71 + 120*x^70 + 106*x^69 + 124*x^68 + 21*x^67 + 120*x^66 + 21*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 82*x^7 + 120*x^6 + 42*x^5 + 124*x^4 + 61*x^3 + 120*x^2 + 125*x + 122, x^75 + 41*x^73 + 70*x^72 + 50*x^71 + 40*x^70 + 10*x^69 + 36*x^68 + 117*x^67 + 104*x^66 + 117*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 114*x^7 + 40*x^6 + 74*x^5 + 36*x^4 + 29*x^3 + 104*x^2 + 93*x + 38, x^75 + 41*x^73 + 78*x^72 + 98*x^71 + 104*x^70 + 26*x^69 + 20*x^68 + 69*x^67 + 40*x^66 + 101*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 34*x^7 + 104*x^6 + 90*x^5 + 20*x^4 + 109*x^3 + 40*x^2 + 77*x + 46, x^75 + 41*x^73 + 42*x^72 + 34*x^71 + 8*x^70 + 58*x^69 + 108*x^68 + 69*x^67 + 40*x^66 + 5*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 98*x^7 + 8*x^6 + 122*x^5 + 108*x^4 + 109*x^3 + 40*x^2 + 109*x + 26, x^75 + 41*x^73 + 6*x^72 + 50*x^71 + 104*x^70 + 74*x^69 + 36*x^68 + 117*x^67 + 40*x^66 + 53*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 114*x^7 + 104*x^6 + 10*x^5 + 36*x^4 + 29*x^3 + 40*x^2 + 29*x + 102, x^75 + 41*x^73 + 6*x^72 + 18*x^71 + 8*x^70 + 42*x^69 + 68*x^68 + 21*x^67 + 8*x^66 + 85*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 82*x^7 + 8*x^6 + 106*x^5 + 68*x^4 + 61*x^3 + 8*x^2 + 61*x + 70, x^75 + 41*x^73 + 38*x^72 + 34*x^71 + 88*x^70 + 58*x^69 + 20*x^68 + 69*x^67 + 120*x^66 + 5*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 98*x^7 + 88*x^6 + 122*x^5 + 20*x^4 + 109*x^3 + 120*x^2 + 109*x + 22, x^75 + 41*x^73 + 126*x^72 + 82*x^71 + 56*x^70 + 10*x^69 + 4*x^68 + 21*x^67 + 24*x^66 + 53*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 18*x^7 + 56*x^6 + 74*x^5 + 4*x^4 + 61*x^3 + 24*x^2 + 29*x + 78, x^75 + 41*x^73 + 114*x^72 + 98*x^71 + 56*x^70 + 90*x^69 + 76*x^68 + 69*x^67 + 56*x^66 + 37*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 34*x^7 + 56*x^6 + 26*x^5 + 76*x^4 + 109*x^3 + 56*x^2 + 13*x + 50, x^75 + 41*x^73 + 70*x^72 + 34*x^71 + 56*x^70 + 58*x^69 + 52*x^68 + 69*x^67 + 24*x^66 + 5*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 98*x^7 + 56*x^6 + 122*x^5 + 52*x^4 + 109*x^3 + 24*x^2 + 109*x + 86, x^75 + 41*x^73 + 6*x^72 + 2*x^71 + 88*x^70 + 26*x^69 + 84*x^68 + 101*x^67 + 120*x^66 + 37*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 66*x^7 + 88*x^6 + 90*x^5 + 84*x^4 + 13*x^3 + 120*x^2 + 13*x + 118, x^75 + 41*x^73 + 122*x^72 + 66*x^71 + 72*x^70 + 90*x^69 + 76*x^68 + 37*x^67 + 104*x^66 + 101*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 2*x^7 + 72*x^6 + 26*x^5 + 76*x^4 + 77*x^3 + 104*x^2 + 77*x + 106, x^75 + 41*x^73 + 22*x^72 + 50*x^71 + 40*x^70 + 10*x^69 + 68*x^68 + 117*x^67 + 104*x^66 + 117*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 114*x^7 + 40*x^6 + 74*x^5 + 68*x^4 + 29*x^3 + 104*x^2 + 93*x + 54, x^75 + 41*x^73 + 106*x^72 + 82*x^71 + 120*x^70 + 106*x^69 + 28*x^68 + 85*x^67 + 120*x^66 + 21*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 18*x^7 + 120*x^6 + 42*x^5 + 28*x^4 + 125*x^3 + 120*x^2 + 125*x + 106, x^75 + 41*x^73 + 122*x^72 + 98*x^71 + 104*x^70 + 122*x^69 + 108*x^68 + 5*x^67 + 72*x^66 + 69*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 34*x^7 + 104*x^6 + 58*x^5 + 108*x^4 + 45*x^3 + 72*x^2 + 45*x + 74, x^75 + 41*x^73 + 18*x^72 + 50*x^71 + 40*x^70 + 42*x^69 + 60*x^68 + 53*x^67 + 8*x^66 + 21*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 114*x^7 + 40*x^6 + 106*x^5 + 60*x^4 + 93*x^3 + 8*x^2 + 125*x + 98, x^75 + 41*x^73 + 102*x^72 + 114*x^71 + 8*x^70 + 74*x^69 + 68*x^68 + 53*x^67 + 8*x^66 + 53*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 50*x^7 + 8*x^6 + 10*x^5 + 68*x^4 + 93*x^3 + 8*x^2 + 29*x + 102, x^75 + 41*x^73 + 62*x^72 + 66*x^71 + 104*x^70 + 58*x^69 + 52*x^68 + 101*x^67 + 40*x^66 + 69*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 2*x^7 + 104*x^6 + 122*x^5 + 52*x^4 + 13*x^3 + 40*x^2 + 45*x + 30, x^75 + 41*x^73 + 66*x^72 + 66*x^71 + 88*x^70 + 58*x^69 + 12*x^68 + 101*x^67 + 24*x^66 + 69*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 2*x^7 + 88*x^6 + 122*x^5 + 12*x^4 + 13*x^3 + 24*x^2 + 45*x + 34, x^75 + 41*x^73 + 58*x^72 + 98*x^71 + 104*x^70 + 58*x^69 + 44*x^68 + 5*x^67 + 72*x^66 + 5*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 34*x^7 + 104*x^6 + 122*x^5 + 44*x^4 + 45*x^3 + 72*x^2 + 109*x + 74, x^75 + 41*x^73 + 78*x^72 + 18*x^71 + 120*x^70 + 74*x^69 + 100*x^68 + 85*x^67 + 88*x^66 + 117*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 82*x^7 + 120*x^6 + 10*x^5 + 100*x^4 + 125*x^3 + 88*x^2 + 93*x + 30, x^75 + 41*x^73 + 122*x^72 + 18*x^71 + 120*x^70 + 42*x^69 + 60*x^68 + 21*x^67 + 120*x^66 + 85*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 82*x^7 + 120*x^6 + 106*x^5 + 60*x^4 + 61*x^3 + 120*x^2 + 61*x + 58, x^75 + 41*x^73 + 2*x^72 + 82*x^71 + 104*x^70 + 74*x^69 + 92*x^68 + 21*x^67 + 72*x^66 + 117*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 18*x^7 + 104*x^6 + 10*x^5 + 92*x^4 + 61*x^3 + 72*x^2 + 93*x + 82, x^75 + 41*x^73 + 98*x^72 + 66*x^71 + 56*x^70 + 58*x^69 + 44*x^68 + 101*x^67 + 56*x^66 + 69*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 2*x^7 + 56*x^6 + 122*x^5 + 44*x^4 + 13*x^3 + 56*x^2 + 45*x + 98, x^75 + 41*x^73 + 110*x^72 + 114*x^71 + 56*x^70 + 106*x^69 + 36*x^68 + 117*x^67 + 24*x^66 + 85*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 50*x^7 + 56*x^6 + 42*x^5 + 36*x^4 + 29*x^3 + 24*x^2 + 61*x + 62, x^75 + 41*x^73 + 2*x^72 + 114*x^71 + 40*x^70 + 106*x^69 + 28*x^68 + 117*x^67 + 8*x^66 + 85*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 50*x^7 + 40*x^6 + 42*x^5 + 28*x^4 + 29*x^3 + 8*x^2 + 61*x + 18, x^75 + 41*x^73 + 126*x^72 + 82*x^71 + 56*x^70 + 74*x^69 + 68*x^68 + 21*x^67 + 24*x^66 + 117*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 18*x^7 + 56*x^6 + 10*x^5 + 68*x^4 + 61*x^3 + 24*x^2 + 93*x + 14, x^75 + 41*x^73 + 58*x^72 + 2*x^71 + 8*x^70 + 26*x^69 + 12*x^68 + 101*x^67 + 40*x^66 + 37*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 66*x^7 + 8*x^6 + 90*x^5 + 12*x^4 + 13*x^3 + 40*x^2 + 13*x + 106, x^75 + 41*x^73 + 74*x^72 + 18*x^71 + 56*x^70 + 42*x^69 + 28*x^68 + 21*x^67 + 56*x^66 + 85*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 82*x^7 + 56*x^6 + 106*x^5 + 28*x^4 + 61*x^3 + 56*x^2 + 61*x + 10, x^75 + 41*x^73 + 86*x^72 + 98*x^71 + 56*x^70 + 58*x^69 + 20*x^68 + 5*x^67 + 24*x^66 + 5*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 34*x^7 + 56*x^6 + 122*x^5 + 20*x^4 + 45*x^3 + 24*x^2 + 109*x + 102, x^75 + 41*x^73 + 54*x^72 + 34*x^71 + 88*x^70 + 58*x^69 + 52*x^68 + 69*x^67 + 120*x^66 + 5*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 98*x^7 + 88*x^6 + 122*x^5 + 52*x^4 + 109*x^3 + 120*x^2 + 109*x + 102, x^75 + 41*x^73 + 18*x^72 + 66*x^71 + 56*x^70 + 122*x^69 + 76*x^68 + 101*x^67 + 56*x^66 + 5*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 2*x^7 + 56*x^6 + 58*x^5 + 76*x^4 + 13*x^3 + 56*x^2 + 109*x + 18, x^75 + 41*x^73 + 94*x^72 + 2*x^71 + 104*x^70 + 122*x^69 + 116*x^68 + 37*x^67 + 40*x^66 + 5*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 66*x^7 + 104*x^6 + 58*x^5 + 116*x^4 + 77*x^3 + 40*x^2 + 109*x + 62, x^75 + 41*x^73 + 6*x^72 + 18*x^71 + 72*x^70 + 106*x^69 + 68*x^68 + 21*x^67 + 72*x^66 + 21*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 82*x^7 + 72*x^6 + 42*x^5 + 68*x^4 + 61*x^3 + 72*x^2 + 125*x + 70, x^75 + 41*x^73 + 42*x^72 + 66*x^71 + 104*x^70 + 26*x^69 + 12*x^68 + 37*x^67 + 72*x^66 + 37*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 2*x^7 + 104*x^6 + 90*x^5 + 12*x^4 + 77*x^3 + 72*x^2 + 13*x + 122, x^75 + 41*x^73 + 66*x^72 + 98*x^71 + 88*x^70 + 90*x^69 + 12*x^68 + 69*x^67 + 24*x^66 + 37*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 34*x^7 + 88*x^6 + 26*x^5 + 12*x^4 + 109*x^3 + 24*x^2 + 13*x + 34, x^75 + 41*x^73 + 90*x^72 + 114*x^71 + 88*x^70 + 10*x^69 + 92*x^68 + 53*x^67 + 24*x^66 + 117*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 50*x^7 + 88*x^6 + 74*x^5 + 92*x^4 + 93*x^3 + 24*x^2 + 93*x + 58, x^75 + 41*x^73 + 54*x^72 + 18*x^71 + 40*x^70 + 42*x^69 + 68*x^68 + 21*x^67 + 104*x^66 + 85*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 82*x^7 + 40*x^6 + 106*x^5 + 68*x^4 + 61*x^3 + 104*x^2 + 61*x + 22, x^75 + 41*x^73 + 50*x^72 + 66*x^71 + 56*x^70 + 122*x^69 + 12*x^68 + 101*x^67 + 56*x^66 + 5*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 2*x^7 + 56*x^6 + 58*x^5 + 12*x^4 + 13*x^3 + 56*x^2 + 109*x + 50, x^75 + 41*x^73 + 10*x^72 + 98*x^71 + 40*x^70 + 58*x^69 + 12*x^68 + 5*x^67 + 8*x^66 + 5*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 34*x^7 + 40*x^6 + 122*x^5 + 12*x^4 + 45*x^3 + 8*x^2 + 109*x + 26, x^75 + 41*x^73 + 18*x^72 + 66*x^71 + 56*x^70 + 58*x^69 + 12*x^68 + 101*x^67 + 56*x^66 + 69*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 2*x^7 + 56*x^6 + 122*x^5 + 12*x^4 + 13*x^3 + 56*x^2 + 45*x + 82, x^75 + 41*x^73 + 118*x^72 + 114*x^71 + 8*x^70 + 10*x^69 + 36*x^68 + 53*x^67 + 8*x^66 + 117*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 50*x^7 + 8*x^6 + 74*x^5 + 36*x^4 + 93*x^3 + 8*x^2 + 93*x + 118, x^75 + 41*x^73 + 50*x^72 + 34*x^71 + 120*x^70 + 26*x^69 + 12*x^68 + 5*x^67 + 120*x^66 + 101*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 98*x^7 + 120*x^6 + 90*x^5 + 12*x^4 + 45*x^3 + 120*x^2 + 77*x + 50, x^75 + 41*x^73 + 126*x^72 + 114*x^71 + 120*x^70 + 42*x^69 + 68*x^68 + 117*x^67 + 88*x^66 + 21*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 50*x^7 + 120*x^6 + 106*x^5 + 68*x^4 + 29*x^3 + 88*x^2 + 125*x + 14, x^75 + 41*x^73 + 10*x^72 + 18*x^71 + 24*x^70 + 42*x^69 + 124*x^68 + 21*x^67 + 88*x^66 + 85*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 82*x^7 + 24*x^6 + 106*x^5 + 124*x^4 + 61*x^3 + 88*x^2 + 61*x + 106, x^75 + 41*x^73 + 114*x^72 + 66*x^71 + 120*x^70 + 58*x^69 + 12*x^68 + 101*x^67 + 120*x^66 + 69*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 2*x^7 + 120*x^6 + 122*x^5 + 12*x^4 + 13*x^3 + 120*x^2 + 45*x + 114, x^75 + 41*x^73 + 110*x^72 + 98*x^71 + 40*x^70 + 26*x^69 + 20*x^68 + 69*x^67 + 104*x^66 + 101*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 34*x^7 + 40*x^6 + 90*x^5 + 20*x^4 + 109*x^3 + 104*x^2 + 77*x + 14, x^75 + 41*x^73 + 14*x^72 + 50*x^71 + 120*x^70 + 106*x^69 + 100*x^68 + 53*x^67 + 88*x^66 + 85*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 114*x^7 + 120*x^6 + 42*x^5 + 100*x^4 + 93*x^3 + 88*x^2 + 61*x + 94, x^75 + 41*x^73 + 82*x^72 + 98*x^71 + 120*x^70 + 26*x^69 + 12*x^68 + 69*x^67 + 120*x^66 + 101*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 34*x^7 + 120*x^6 + 90*x^5 + 12*x^4 + 109*x^3 + 120*x^2 + 77*x + 18, x^75 + 41*x^73 + 70*x^72 + 98*x^71 + 56*x^70 + 58*x^69 + 116*x^68 + 5*x^67 + 24*x^66 + 5*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 34*x^7 + 56*x^6 + 122*x^5 + 116*x^4 + 45*x^3 + 24*x^2 + 109*x + 22, x^75 + 41*x^73 + 22*x^72 + 2*x^71 + 24*x^70 + 26*x^69 + 52*x^68 + 101*x^67 + 56*x^66 + 37*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 66*x^7 + 24*x^6 + 90*x^5 + 52*x^4 + 13*x^3 + 56*x^2 + 13*x + 6, x^75 + 41*x^73 + 34*x^72 + 98*x^71 + 88*x^70 + 90*x^69 + 76*x^68 + 69*x^67 + 24*x^66 + 37*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 34*x^7 + 88*x^6 + 26*x^5 + 76*x^4 + 109*x^3 + 24*x^2 + 13*x + 2, x^75 + 41*x^73 + 30*x^72 + 66*x^71 + 72*x^70 + 58*x^69 + 84*x^68 + 101*x^67 + 72*x^66 + 69*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 2*x^7 + 72*x^6 + 122*x^5 + 84*x^4 + 13*x^3 + 72*x^2 + 45*x + 30, x^75 + 41*x^73 + 30*x^72 + 66*x^71 + 40*x^70 + 122*x^69 + 116*x^68 + 101*x^67 + 104*x^66 + 5*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 2*x^7 + 40*x^6 + 58*x^5 + 116*x^4 + 13*x^3 + 104*x^2 + 109*x + 126, x^75 + 41*x^73 + 26*x^72 + 82*x^71 + 24*x^70 + 42*x^69 + 92*x^68 + 85*x^67 + 88*x^66 + 85*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 18*x^7 + 24*x^6 + 106*x^5 + 92*x^4 + 125*x^3 + 88*x^2 + 61*x + 122, x^75 + 41*x^73 + 58*x^72 + 50*x^71 + 88*x^70 + 10*x^69 + 92*x^68 + 117*x^67 + 24*x^66 + 117*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 114*x^7 + 88*x^6 + 74*x^5 + 92*x^4 + 29*x^3 + 24*x^2 + 93*x + 90, x^75 + 41*x^73 + 62*x^72 + 2*x^71 + 104*x^70 + 122*x^69 + 52*x^68 + 37*x^67 + 40*x^66 + 5*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 66*x^7 + 104*x^6 + 58*x^5 + 52*x^4 + 77*x^3 + 40*x^2 + 109*x + 30, x^75 + 41*x^73 + 46*x^72 + 66*x^71 + 72*x^70 + 122*x^69 + 52*x^68 + 101*x^67 + 72*x^66 + 5*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 2*x^7 + 72*x^6 + 58*x^5 + 52*x^4 + 13*x^3 + 72*x^2 + 109*x + 46, x^75 + 41*x^73 + 34*x^72 + 50*x^71 + 104*x^70 + 106*x^69 + 92*x^68 + 53*x^67 + 72*x^66 + 85*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 114*x^7 + 104*x^6 + 42*x^5 + 92*x^4 + 93*x^3 + 72*x^2 + 61*x + 50, x^75 + 41*x^73 + 38*x^72 + 50*x^71 + 8*x^70 + 74*x^69 + 4*x^68 + 117*x^67 + 8*x^66 + 53*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 114*x^7 + 8*x^6 + 10*x^5 + 4*x^4 + 29*x^3 + 8*x^2 + 29*x + 102, x^75 + 41*x^73 + 50*x^72 + 82*x^71 + 40*x^70 + 74*x^69 + 124*x^68 + 21*x^67 + 8*x^66 + 117*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 18*x^7 + 40*x^6 + 10*x^5 + 124*x^4 + 61*x^3 + 8*x^2 + 93*x + 2, x^75 + 41*x^73 + 106*x^72 + 82*x^71 + 56*x^70 + 42*x^69 + 28*x^68 + 85*x^67 + 56*x^66 + 85*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 18*x^7 + 56*x^6 + 106*x^5 + 28*x^4 + 125*x^3 + 56*x^2 + 61*x + 106, x^75 + 41*x^73 + 26*x^72 + 66*x^71 + 8*x^70 + 90*x^69 + 76*x^68 + 37*x^67 + 40*x^66 + 101*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 2*x^7 + 8*x^6 + 26*x^5 + 76*x^4 + 77*x^3 + 40*x^2 + 77*x + 74, x^75 + 41*x^73 + 10*x^72 + 98*x^71 + 40*x^70 + 122*x^69 + 76*x^68 + 5*x^67 + 8*x^66 + 69*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 34*x^7 + 40*x^6 + 58*x^5 + 76*x^4 + 45*x^3 + 8*x^2 + 45*x + 90, x^75 + 41*x^73 + 86*x^72 + 98*x^71 + 24*x^70 + 122*x^69 + 52*x^68 + 5*x^67 + 56*x^66 + 69*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 34*x^7 + 24*x^6 + 58*x^5 + 52*x^4 + 45*x^3 + 56*x^2 + 45*x + 70, x^75 + 41*x^73 + 34*x^72 + 34*x^71 + 56*x^70 + 90*x^69 + 108*x^68 + 5*x^67 + 56*x^66 + 37*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 98*x^7 + 56*x^6 + 26*x^5 + 108*x^4 + 45*x^3 + 56*x^2 + 13*x + 98, x^75 + 41*x^73 + 98*x^72 + 2*x^71 + 56*x^70 + 58*x^69 + 108*x^68 + 37*x^67 + 56*x^66 + 69*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 66*x^7 + 56*x^6 + 122*x^5 + 108*x^4 + 77*x^3 + 56*x^2 + 45*x + 34, x^75 + 41*x^73 + 14*x^72 + 2*x^71 + 104*x^70 + 122*x^69 + 84*x^68 + 37*x^67 + 40*x^66 + 5*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 66*x^7 + 104*x^6 + 58*x^5 + 84*x^4 + 77*x^3 + 40*x^2 + 109*x + 46, x^75 + 41*x^73 + 118*x^72 + 98*x^71 + 24*x^70 + 58*x^69 + 52*x^68 + 5*x^67 + 56*x^66 + 5*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 34*x^7 + 24*x^6 + 122*x^5 + 52*x^4 + 45*x^3 + 56*x^2 + 109*x + 38, x^75 + 41*x^73 + 82*x^72 + 18*x^71 + 104*x^70 + 74*x^69 + 60*x^68 + 85*x^67 + 72*x^66 + 117*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 82*x^7 + 104*x^6 + 10*x^5 + 60*x^4 + 125*x^3 + 72*x^2 + 93*x + 34, x^75 + 41*x^73 + 62*x^72 + 82*x^71 + 24*x^70 + 10*x^69 + 100*x^68 + 21*x^67 + 56*x^66 + 53*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 18*x^7 + 24*x^6 + 74*x^5 + 100*x^4 + 61*x^3 + 56*x^2 + 29*x + 46, x^75 + 41*x^73 + 86*x^72 + 114*x^71 + 104*x^70 + 10*x^69 + 68*x^68 + 53*x^67 + 40*x^66 + 117*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 50*x^7 + 104*x^6 + 74*x^5 + 68*x^4 + 93*x^3 + 40*x^2 + 93*x + 118, x^75 + 41*x^73 + 86*x^72 + 18*x^71 + 8*x^70 + 42*x^69 + 100*x^68 + 21*x^67 + 8*x^66 + 85*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 82*x^7 + 8*x^6 + 106*x^5 + 100*x^4 + 61*x^3 + 8*x^2 + 61*x + 86, x^75 + 41*x^73 + 34*x^72 + 66*x^71 + 120*x^70 + 122*x^69 + 44*x^68 + 101*x^67 + 120*x^66 + 5*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 2*x^7 + 120*x^6 + 58*x^5 + 44*x^4 + 13*x^3 + 120*x^2 + 109*x + 34, x^75 + 41*x^73 + 94*x^72 + 98*x^71 + 72*x^70 + 26*x^69 + 20*x^68 + 69*x^67 + 72*x^66 + 101*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 34*x^7 + 72*x^6 + 90*x^5 + 20*x^4 + 109*x^3 + 72*x^2 + 77*x + 30, x^75 + 41*x^73 + 2*x^72 + 50*x^71 + 8*x^70 + 42*x^69 + 124*x^68 + 53*x^67 + 40*x^66 + 21*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 114*x^7 + 8*x^6 + 106*x^5 + 124*x^4 + 93*x^3 + 40*x^2 + 125*x + 50, x^75 + 41*x^73 + 42*x^72 + 82*x^71 + 24*x^70 + 106*x^69 + 60*x^68 + 85*x^67 + 88*x^66 + 21*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 18*x^7 + 24*x^6 + 42*x^5 + 60*x^4 + 125*x^3 + 88*x^2 + 125*x + 10, x^75 + 41*x^73 + 70*x^72 + 50*x^71 + 8*x^70 + 74*x^69 + 68*x^68 + 117*x^67 + 8*x^66 + 53*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 114*x^7 + 8*x^6 + 10*x^5 + 68*x^4 + 29*x^3 + 8*x^2 + 29*x + 6, x^75 + 41*x^73 + 74*x^72 + 2*x^71 + 72*x^70 + 90*x^69 + 44*x^68 + 101*x^67 + 104*x^66 + 101*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 66*x^7 + 72*x^6 + 26*x^5 + 44*x^4 + 13*x^3 + 104*x^2 + 77*x + 58, x^75 + 41*x^73 + 42*x^72 + 34*x^71 + 72*x^70 + 58*x^69 + 44*x^68 + 69*x^67 + 104*x^66 + 5*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 98*x^7 + 72*x^6 + 122*x^5 + 44*x^4 + 109*x^3 + 104*x^2 + 109*x + 90, x^75 + 41*x^73 + 74*x^72 + 50*x^71 + 24*x^70 + 10*x^69 + 60*x^68 + 117*x^67 + 88*x^66 + 117*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 114*x^7 + 24*x^6 + 74*x^5 + 60*x^4 + 29*x^3 + 88*x^2 + 93*x + 106, x^75 + 41*x^73 + 94*x^72 + 114*x^71 + 24*x^70 + 42*x^69 + 36*x^68 + 117*x^67 + 56*x^66 + 21*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 50*x^7 + 24*x^6 + 106*x^5 + 36*x^4 + 29*x^3 + 56*x^2 + 125*x + 78, x^75 + 41*x^73 + 98*x^72 + 2*x^71 + 24*x^70 + 122*x^69 + 12*x^68 + 37*x^67 + 88*x^66 + 5*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 66*x^7 + 24*x^6 + 58*x^5 + 12*x^4 + 77*x^3 + 88*x^2 + 109*x + 2, x^75 + 41*x^73 + 62*x^72 + 50*x^71 + 24*x^70 + 42*x^69 + 36*x^68 + 53*x^67 + 56*x^66 + 21*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 114*x^7 + 24*x^6 + 106*x^5 + 36*x^4 + 93*x^3 + 56*x^2 + 125*x + 110, x^75 + 41*x^73 + 94*x^72 + 114*x^71 + 88*x^70 + 106*x^69 + 36*x^68 + 117*x^67 + 120*x^66 + 85*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 50*x^7 + 88*x^6 + 42*x^5 + 36*x^4 + 29*x^3 + 120*x^2 + 61*x + 78, x^75 + 41*x^73 + 62*x^72 + 98*x^71 + 40*x^70 + 26*x^69 + 52*x^68 + 69*x^67 + 104*x^66 + 101*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 34*x^7 + 40*x^6 + 90*x^5 + 52*x^4 + 109*x^3 + 104*x^2 + 77*x + 30, x^75 + 41*x^73 + 62*x^72 + 50*x^71 + 88*x^70 + 106*x^69 + 36*x^68 + 53*x^67 + 120*x^66 + 85*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 114*x^7 + 88*x^6 + 42*x^5 + 36*x^4 + 93*x^3 + 120*x^2 + 61*x + 110, x^75 + 41*x^73 + 14*x^72 + 18*x^71 + 56*x^70 + 74*x^69 + 36*x^68 + 85*x^67 + 24*x^66 + 117*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 82*x^7 + 56*x^6 + 10*x^5 + 36*x^4 + 125*x^3 + 24*x^2 + 93*x + 30, x^75 + 41*x^73 + 70*x^72 + 34*x^71 + 56*x^70 + 122*x^69 + 116*x^68 + 69*x^67 + 24*x^66 + 69*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 98*x^7 + 56*x^6 + 58*x^5 + 116*x^4 + 109*x^3 + 24*x^2 + 45*x + 22, x^75 + 41*x^73 + 18*x^72 + 50*x^71 + 8*x^70 + 42*x^69 + 28*x^68 + 53*x^67 + 40*x^66 + 21*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 114*x^7 + 8*x^6 + 106*x^5 + 28*x^4 + 93*x^3 + 40*x^2 + 125*x + 2, x^75 + 41*x^73 + 90*x^72 + 82*x^71 + 24*x^70 + 42*x^69 + 92*x^68 + 85*x^67 + 88*x^66 + 85*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 18*x^7 + 24*x^6 + 106*x^5 + 92*x^4 + 125*x^3 + 88*x^2 + 61*x + 58, x^75 + 41*x^73 + 42*x^72 + 34*x^71 + 8*x^70 + 122*x^69 + 44*x^68 + 69*x^67 + 40*x^66 + 69*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 98*x^7 + 8*x^6 + 58*x^5 + 44*x^4 + 109*x^3 + 40*x^2 + 45*x + 90, x^75 + 41*x^73 + 66*x^72 + 98*x^71 + 120*x^70 + 90*x^69 + 44*x^68 + 69*x^67 + 120*x^66 + 37*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 34*x^7 + 120*x^6 + 26*x^5 + 44*x^4 + 109*x^3 + 120*x^2 + 13*x + 2, x^75 + 41*x^73 + 110*x^72 + 2*x^71 + 8*x^70 + 58*x^69 + 116*x^68 + 37*x^67 + 8*x^66 + 69*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 66*x^7 + 8*x^6 + 122*x^5 + 116*x^4 + 77*x^3 + 8*x^2 + 45*x + 46, x^75 + 41*x^73 + 38*x^72 + 18*x^71 + 104*x^70 + 42*x^69 + 100*x^68 + 21*x^67 + 40*x^66 + 85*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 82*x^7 + 104*x^6 + 106*x^5 + 100*x^4 + 61*x^3 + 40*x^2 + 61*x + 6, x^75 + 41*x^73 + 86*x^72 + 18*x^71 + 104*x^70 + 42*x^69 + 68*x^68 + 21*x^67 + 40*x^66 + 85*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 82*x^7 + 104*x^6 + 106*x^5 + 68*x^4 + 61*x^3 + 40*x^2 + 61*x + 118, x^75 + 41*x^73 + 62*x^72 + 2*x^71 + 8*x^70 + 58*x^69 + 20*x^68 + 37*x^67 + 8*x^66 + 69*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 66*x^7 + 8*x^6 + 122*x^5 + 20*x^4 + 77*x^3 + 8*x^2 + 45*x + 62, x^75 + 41*x^73 + 6*x^72 + 50*x^71 + 8*x^70 + 74*x^69 + 68*x^68 + 117*x^67 + 8*x^66 + 53*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 114*x^7 + 8*x^6 + 10*x^5 + 68*x^4 + 29*x^3 + 8*x^2 + 29*x + 70, x^75 + 41*x^73 + 114*x^72 + 66*x^71 + 24*x^70 + 58*x^69 + 44*x^68 + 101*x^67 + 88*x^66 + 69*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 2*x^7 + 24*x^6 + 122*x^5 + 44*x^4 + 13*x^3 + 88*x^2 + 45*x + 82, x^75 + 41*x^73 + 118*x^72 + 2*x^71 + 88*x^70 + 26*x^69 + 52*x^68 + 101*x^67 + 120*x^66 + 37*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 66*x^7 + 88*x^6 + 90*x^5 + 52*x^4 + 13*x^3 + 120*x^2 + 13*x + 38, x^75 + 41*x^73 + 26*x^72 + 98*x^71 + 8*x^70 + 122*x^69 + 76*x^68 + 5*x^67 + 40*x^66 + 69*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 34*x^7 + 8*x^6 + 58*x^5 + 76*x^4 + 45*x^3 + 40*x^2 + 45*x + 74, x^75 + 41*x^73 + 10*x^72 + 114*x^71 + 24*x^70 + 74*x^69 + 60*x^68 + 53*x^67 + 88*x^66 + 53*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 50*x^7 + 24*x^6 + 10*x^5 + 60*x^4 + 93*x^3 + 88*x^2 + 29*x + 42, x^75 + 41*x^73 + 106*x^72 + 34*x^71 + 104*x^70 + 58*x^69 + 76*x^68 + 69*x^67 + 72*x^66 + 5*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 98*x^7 + 104*x^6 + 122*x^5 + 76*x^4 + 109*x^3 + 72*x^2 + 109*x + 122, x^75 + 41*x^73 + 86*x^72 + 50*x^71 + 104*x^70 + 10*x^69 + 4*x^68 + 117*x^67 + 40*x^66 + 117*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 114*x^7 + 104*x^6 + 74*x^5 + 4*x^4 + 29*x^3 + 40*x^2 + 93*x + 54, x^75 + 41*x^73 + 106*x^72 + 50*x^71 + 24*x^70 + 10*x^69 + 124*x^68 + 117*x^67 + 88*x^66 + 117*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 114*x^7 + 24*x^6 + 74*x^5 + 124*x^4 + 29*x^3 + 88*x^2 + 93*x + 10, x^75 + 41*x^73 + 118*x^72 + 18*x^71 + 8*x^70 + 106*x^69 + 100*x^68 + 21*x^67 + 8*x^66 + 21*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 82*x^7 + 8*x^6 + 42*x^5 + 100*x^4 + 61*x^3 + 8*x^2 + 125*x + 54, x^75 + 41*x^73 + 54*x^72 + 82*x^71 + 40*x^70 + 106*x^69 + 68*x^68 + 85*x^67 + 104*x^66 + 21*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 18*x^7 + 40*x^6 + 42*x^5 + 68*x^4 + 125*x^3 + 104*x^2 + 125*x + 22, x^75 + 41*x^73 + 50*x^72 + 114*x^71 + 72*x^70 + 42*x^69 + 92*x^68 + 117*x^67 + 104*x^66 + 21*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 50*x^7 + 72*x^6 + 106*x^5 + 92*x^4 + 29*x^3 + 104*x^2 + 125*x + 34, x^75 + 41*x^73 + 86*x^72 + 66*x^71 + 24*x^70 + 26*x^69 + 116*x^68 + 37*x^67 + 56*x^66 + 37*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 2*x^7 + 24*x^6 + 90*x^5 + 116*x^4 + 77*x^3 + 56*x^2 + 13*x + 6, x^75 + 41*x^73 + 10*x^72 + 34*x^71 + 40*x^70 + 58*x^69 + 76*x^68 + 69*x^67 + 8*x^66 + 5*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 98*x^7 + 40*x^6 + 122*x^5 + 76*x^4 + 109*x^3 + 8*x^2 + 109*x + 90, x^75 + 41*x^73 + 30*x^72 + 50*x^71 + 24*x^70 + 42*x^69 + 100*x^68 + 53*x^67 + 56*x^66 + 21*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 114*x^7 + 24*x^6 + 106*x^5 + 100*x^4 + 93*x^3 + 56*x^2 + 125*x + 78, x^75 + 41*x^73 + 106*x^72 + 66*x^71 + 8*x^70 + 90*x^69 + 108*x^68 + 37*x^67 + 40*x^66 + 101*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 2*x^7 + 8*x^6 + 26*x^5 + 108*x^4 + 77*x^3 + 40*x^2 + 77*x + 90, x^75 + 41*x^73 + 14*x^72 + 2*x^71 + 8*x^70 + 122*x^69 + 116*x^68 + 37*x^67 + 8*x^66 + 5*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 66*x^7 + 8*x^6 + 58*x^5 + 116*x^4 + 77*x^3 + 8*x^2 + 109*x + 14, x^75 + 41*x^73 + 14*x^72 + 50*x^71 + 24*x^70 + 106*x^69 + 4*x^68 + 53*x^67 + 56*x^66 + 85*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 114*x^7 + 24*x^6 + 42*x^5 + 4*x^4 + 93*x^3 + 56*x^2 + 61*x + 62, x^75 + 41*x^73 + 66*x^72 + 98*x^71 + 56*x^70 + 26*x^69 + 44*x^68 + 69*x^67 + 56*x^66 + 101*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 34*x^7 + 56*x^6 + 90*x^5 + 44*x^4 + 109*x^3 + 56*x^2 + 77*x + 2, x^75 + 41*x^73 + 94*x^72 + 34*x^71 + 72*x^70 + 26*x^69 + 84*x^68 + 5*x^67 + 72*x^66 + 101*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 98*x^7 + 72*x^6 + 90*x^5 + 84*x^4 + 45*x^3 + 72*x^2 + 77*x + 94, x^75 + 41*x^73 + 94*x^72 + 2*x^71 + 40*x^70 + 58*x^69 + 116*x^68 + 37*x^67 + 104*x^66 + 69*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 66*x^7 + 40*x^6 + 122*x^5 + 116*x^4 + 77*x^3 + 104*x^2 + 45*x + 62, x^75 + 41*x^73 + 54*x^72 + 66*x^71 + 56*x^70 + 26*x^69 + 84*x^68 + 37*x^67 + 24*x^66 + 37*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 2*x^7 + 56*x^6 + 90*x^5 + 84*x^4 + 77*x^3 + 24*x^2 + 13*x + 70, x^75 + 41*x^73 + 74*x^72 + 66*x^71 + 8*x^70 + 90*x^69 + 44*x^68 + 37*x^67 + 40*x^66 + 101*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 2*x^7 + 8*x^6 + 26*x^5 + 44*x^4 + 77*x^3 + 40*x^2 + 77*x + 58, x^75 + 41*x^73 + 114*x^72 + 66*x^71 + 24*x^70 + 122*x^69 + 108*x^68 + 101*x^67 + 88*x^66 + 5*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 2*x^7 + 24*x^6 + 58*x^5 + 108*x^4 + 13*x^3 + 88*x^2 + 109*x + 18, x^75 + 41*x^73 + 2*x^72 + 34*x^71 + 120*x^70 + 26*x^69 + 44*x^68 + 5*x^67 + 120*x^66 + 101*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 98*x^7 + 120*x^6 + 90*x^5 + 44*x^4 + 45*x^3 + 120*x^2 + 77*x + 66, x^75 + 41*x^73 + 86*x^72 + 34*x^71 + 88*x^70 + 122*x^69 + 52*x^68 + 69*x^67 + 120*x^66 + 69*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 98*x^7 + 88*x^6 + 58*x^5 + 52*x^4 + 109*x^3 + 120*x^2 + 45*x + 70, x^75 + 41*x^73 + 90*x^72 + 2*x^71 + 8*x^70 + 26*x^69 + 76*x^68 + 101*x^67 + 40*x^66 + 37*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 66*x^7 + 8*x^6 + 90*x^5 + 76*x^4 + 13*x^3 + 40*x^2 + 13*x + 10, x^75 + 41*x^73 + 54*x^72 + 2*x^71 + 88*x^70 + 90*x^69 + 116*x^68 + 101*x^67 + 120*x^66 + 101*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 66*x^7 + 88*x^6 + 26*x^5 + 116*x^4 + 13*x^3 + 120*x^2 + 77*x + 38, x^75 + 41*x^73 + 118*x^72 + 98*x^71 + 120*x^70 + 58*x^69 + 20*x^68 + 5*x^67 + 88*x^66 + 5*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 34*x^7 + 120*x^6 + 122*x^5 + 20*x^4 + 45*x^3 + 88*x^2 + 109*x + 70, x^75 + 41*x^73 + 110*x^72 + 18*x^71 + 56*x^70 + 10*x^69 + 36*x^68 + 85*x^67 + 24*x^66 + 53*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 82*x^7 + 56*x^6 + 74*x^5 + 36*x^4 + 125*x^3 + 24*x^2 + 29*x + 62, x^75 + 41*x^73 + 74*x^72 + 98*x^71 + 8*x^70 + 58*x^69 + 108*x^68 + 5*x^67 + 40*x^66 + 5*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 34*x^7 + 8*x^6 + 122*x^5 + 108*x^4 + 45*x^3 + 40*x^2 + 109*x + 122, x^75 + 41*x^73 + 110*x^72 + 34*x^71 + 72*x^70 + 26*x^69 + 116*x^68 + 5*x^67 + 72*x^66 + 101*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 98*x^7 + 72*x^6 + 90*x^5 + 116*x^4 + 45*x^3 + 72*x^2 + 77*x + 46, x^75 + 41*x^73 + 26*x^72 + 82*x^71 + 120*x^70 + 42*x^69 + 60*x^68 + 85*x^67 + 120*x^66 + 85*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 18*x^7 + 120*x^6 + 106*x^5 + 60*x^4 + 125*x^3 + 120*x^2 + 61*x + 26, x^75 + 41*x^73 + 126*x^72 + 2*x^71 + 72*x^70 + 122*x^69 + 20*x^68 + 37*x^67 + 72*x^66 + 5*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 66*x^7 + 72*x^6 + 58*x^5 + 20*x^4 + 77*x^3 + 72*x^2 + 109*x + 126, x^75 + 41*x^73 + 114*x^72 + 34*x^71 + 24*x^70 + 26*x^69 + 44*x^68 + 5*x^67 + 88*x^66 + 101*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 98*x^7 + 24*x^6 + 90*x^5 + 44*x^4 + 45*x^3 + 88*x^2 + 77*x + 82, x^75 + 41*x^73 + 114*x^72 + 98*x^71 + 120*x^70 + 26*x^69 + 76*x^68 + 69*x^67 + 120*x^66 + 101*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 34*x^7 + 120*x^6 + 90*x^5 + 76*x^4 + 109*x^3 + 120*x^2 + 77*x + 50, x^75 + 41*x^73 + 54*x^72 + 50*x^71 + 40*x^70 + 74*x^69 + 68*x^68 + 117*x^67 + 104*x^66 + 53*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 114*x^7 + 40*x^6 + 10*x^5 + 68*x^4 + 29*x^3 + 104*x^2 + 29*x + 22, x^75 + 41*x^73 + 34*x^72 + 98*x^71 + 56*x^70 + 90*x^69 + 44*x^68 + 69*x^67 + 56*x^66 + 37*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 34*x^7 + 56*x^6 + 26*x^5 + 44*x^4 + 109*x^3 + 56*x^2 + 13*x + 34, x^75 + 41*x^73 + 118*x^72 + 66*x^71 + 120*x^70 + 90*x^69 + 84*x^68 + 37*x^67 + 88*x^66 + 101*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 2*x^7 + 120*x^6 + 26*x^5 + 84*x^4 + 77*x^3 + 88*x^2 + 77*x + 6, x^75 + 41*x^73 + 86*x^72 + 98*x^71 + 24*x^70 + 58*x^69 + 116*x^68 + 5*x^67 + 56*x^66 + 5*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 34*x^7 + 24*x^6 + 122*x^5 + 116*x^4 + 45*x^3 + 56*x^2 + 109*x + 6, x^75 + 41*x^73 + 118*x^72 + 66*x^71 + 24*x^70 + 26*x^69 + 52*x^68 + 37*x^67 + 56*x^66 + 37*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 2*x^7 + 24*x^6 + 90*x^5 + 52*x^4 + 77*x^3 + 56*x^2 + 13*x + 38, x^75 + 41*x^73 + 78*x^72 + 34*x^71 + 104*x^70 + 90*x^69 + 20*x^68 + 5*x^67 + 40*x^66 + 37*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 98*x^7 + 104*x^6 + 26*x^5 + 20*x^4 + 45*x^3 + 40*x^2 + 13*x + 46, x^75 + 41*x^73 + 26*x^72 + 34*x^71 + 72*x^70 + 58*x^69 + 12*x^68 + 69*x^67 + 104*x^66 + 5*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 98*x^7 + 72*x^6 + 122*x^5 + 12*x^4 + 109*x^3 + 104*x^2 + 109*x + 10, x^75 + 41*x^73 + 82*x^72 + 18*x^71 + 104*x^70 + 10*x^69 + 124*x^68 + 85*x^67 + 72*x^66 + 53*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 82*x^7 + 104*x^6 + 74*x^5 + 124*x^4 + 125*x^3 + 72*x^2 + 29*x + 98, x^75 + 41*x^73 + 66*x^72 + 114*x^71 + 40*x^70 + 106*x^69 + 28*x^68 + 117*x^67 + 8*x^66 + 85*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 50*x^7 + 40*x^6 + 42*x^5 + 28*x^4 + 29*x^3 + 8*x^2 + 61*x + 82, x^75 + 41*x^73 + 66*x^72 + 2*x^71 + 24*x^70 + 122*x^69 + 76*x^68 + 37*x^67 + 88*x^66 + 5*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 66*x^7 + 24*x^6 + 58*x^5 + 76*x^4 + 77*x^3 + 88*x^2 + 109*x + 98, x^75 + 41*x^73 + 94*x^72 + 98*x^71 + 8*x^70 + 26*x^69 + 84*x^68 + 69*x^67 + 8*x^66 + 101*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 34*x^7 + 8*x^6 + 90*x^5 + 84*x^4 + 109*x^3 + 8*x^2 + 77*x + 94, x^75 + 41*x^73 + 126*x^72 + 50*x^71 + 24*x^70 + 42*x^69 + 36*x^68 + 53*x^67 + 56*x^66 + 21*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 114*x^7 + 24*x^6 + 106*x^5 + 36*x^4 + 93*x^3 + 56*x^2 + 125*x + 46, x^75 + 41*x^73 + 126*x^72 + 50*x^71 + 88*x^70 + 106*x^69 + 36*x^68 + 53*x^67 + 120*x^66 + 85*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 114*x^7 + 88*x^6 + 42*x^5 + 36*x^4 + 93*x^3 + 120*x^2 + 61*x + 46, x^75 + 41*x^73 + 102*x^72 + 18*x^71 + 8*x^70 + 106*x^69 + 68*x^68 + 21*x^67 + 8*x^66 + 21*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 82*x^7 + 8*x^6 + 42*x^5 + 68*x^4 + 61*x^3 + 8*x^2 + 125*x + 102, x^75 + 41*x^73 + 66*x^72 + 82*x^71 + 40*x^70 + 10*x^69 + 92*x^68 + 21*x^67 + 8*x^66 + 53*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 18*x^7 + 40*x^6 + 74*x^5 + 92*x^4 + 61*x^3 + 8*x^2 + 29*x + 18, x^75 + 41*x^73 + 106*x^72 + 98*x^71 + 8*x^70 + 122*x^69 + 108*x^68 + 5*x^67 + 40*x^66 + 69*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 34*x^7 + 8*x^6 + 58*x^5 + 108*x^4 + 45*x^3 + 40*x^2 + 45*x + 90, x^75 + 41*x^73 + 62*x^72 + 2*x^71 + 40*x^70 + 58*x^69 + 52*x^68 + 37*x^67 + 104*x^66 + 69*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 66*x^7 + 40*x^6 + 122*x^5 + 52*x^4 + 77*x^3 + 104*x^2 + 45*x + 30, x^75 + 41*x^73 + 2*x^72 + 82*x^71 + 40*x^70 + 10*x^69 + 92*x^68 + 21*x^67 + 8*x^66 + 53*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 18*x^7 + 40*x^6 + 74*x^5 + 92*x^4 + 61*x^3 + 8*x^2 + 29*x + 82, x^75 + 41*x^73 + 34*x^72 + 50*x^71 + 40*x^70 + 42*x^69 + 92*x^68 + 53*x^67 + 8*x^66 + 21*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 114*x^7 + 40*x^6 + 106*x^5 + 92*x^4 + 93*x^3 + 8*x^2 + 125*x + 50, x^75 + 41*x^73 + 74*x^72 + 18*x^71 + 88*x^70 + 42*x^69 + 60*x^68 + 21*x^67 + 24*x^66 + 85*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 82*x^7 + 88*x^6 + 106*x^5 + 60*x^4 + 61*x^3 + 24*x^2 + 61*x + 106, x^75 + 41*x^73 + 54*x^72 + 82*x^71 + 8*x^70 + 42*x^69 + 100*x^68 + 85*x^67 + 8*x^66 + 85*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 18*x^7 + 8*x^6 + 106*x^5 + 100*x^4 + 125*x^3 + 8*x^2 + 61*x + 118, x^75 + 41*x^73 + 110*x^72 + 98*x^71 + 8*x^70 + 26*x^69 + 116*x^68 + 69*x^67 + 8*x^66 + 101*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 34*x^7 + 8*x^6 + 90*x^5 + 116*x^4 + 109*x^3 + 8*x^2 + 77*x + 46, x^75 + 41*x^73 + 78*x^72 + 114*x^71 + 120*x^70 + 42*x^69 + 100*x^68 + 117*x^67 + 88*x^66 + 21*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 50*x^7 + 120*x^6 + 106*x^5 + 100*x^4 + 29*x^3 + 88*x^2 + 125*x + 30, x^75 + 41*x^73 + 90*x^72 + 18*x^71 + 88*x^70 + 42*x^69 + 92*x^68 + 21*x^67 + 24*x^66 + 85*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 82*x^7 + 88*x^6 + 106*x^5 + 92*x^4 + 61*x^3 + 24*x^2 + 61*x + 58, x^75 + 41*x^73 + 86*x^72 + 114*x^71 + 40*x^70 + 10*x^69 + 4*x^68 + 53*x^67 + 104*x^66 + 117*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 50*x^7 + 40*x^6 + 74*x^5 + 4*x^4 + 93*x^3 + 104*x^2 + 93*x + 54, x^75 + 41*x^73 + 90*x^72 + 34*x^71 + 40*x^70 + 58*x^69 + 108*x^68 + 69*x^67 + 8*x^66 + 5*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 98*x^7 + 40*x^6 + 122*x^5 + 108*x^4 + 109*x^3 + 8*x^2 + 109*x + 106, x^75 + 41*x^73 + 38*x^72 + 82*x^71 + 104*x^70 + 42*x^69 + 36*x^68 + 85*x^67 + 40*x^66 + 85*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 18*x^7 + 104*x^6 + 106*x^5 + 36*x^4 + 125*x^3 + 40*x^2 + 61*x + 70, x^75 + 41*x^73 + 126*x^72 + 82*x^71 + 24*x^70 + 10*x^69 + 100*x^68 + 21*x^67 + 56*x^66 + 53*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 18*x^7 + 24*x^6 + 74*x^5 + 100*x^4 + 61*x^3 + 56*x^2 + 29*x + 110, x^75 + 41*x^73 + 126*x^72 + 34*x^71 + 104*x^70 + 90*x^69 + 116*x^68 + 5*x^67 + 40*x^66 + 37*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 98*x^7 + 104*x^6 + 26*x^5 + 116*x^4 + 45*x^3 + 40*x^2 + 13*x + 30, x^75 + 41*x^73 + 14*x^72 + 2*x^71 + 40*x^70 + 58*x^69 + 84*x^68 + 37*x^67 + 104*x^66 + 69*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 66*x^7 + 40*x^6 + 122*x^5 + 84*x^4 + 77*x^3 + 104*x^2 + 45*x + 46, x^75 + 41*x^73 + 54*x^72 + 18*x^71 + 72*x^70 + 42*x^69 + 100*x^68 + 21*x^67 + 72*x^66 + 85*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 82*x^7 + 72*x^6 + 106*x^5 + 100*x^4 + 61*x^3 + 72*x^2 + 61*x + 118, x^75 + 41*x^73 + 34*x^72 + 114*x^71 + 8*x^70 + 106*x^69 + 60*x^68 + 117*x^67 + 40*x^66 + 85*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 50*x^7 + 8*x^6 + 42*x^5 + 60*x^4 + 29*x^3 + 40*x^2 + 61*x + 82, x^75 + 41*x^73 + 10*x^72 + 2*x^71 + 72*x^70 + 90*x^69 + 44*x^68 + 101*x^67 + 104*x^66 + 101*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 66*x^7 + 72*x^6 + 26*x^5 + 44*x^4 + 13*x^3 + 104*x^2 + 77*x + 122, x^75 + 41*x^73 + 38*x^72 + 98*x^71 + 120*x^70 + 58*x^69 + 116*x^68 + 5*x^67 + 88*x^66 + 5*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 34*x^7 + 120*x^6 + 122*x^5 + 116*x^4 + 45*x^3 + 88*x^2 + 109*x + 54, x^75 + 41*x^73 + 62*x^72 + 98*x^71 + 104*x^70 + 26*x^69 + 116*x^68 + 69*x^67 + 40*x^66 + 101*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 34*x^7 + 104*x^6 + 90*x^5 + 116*x^4 + 109*x^3 + 40*x^2 + 77*x + 94, x^75 + 41*x^73 + 78*x^72 + 50*x^71 + 56*x^70 + 42*x^69 + 100*x^68 + 53*x^67 + 24*x^66 + 21*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 114*x^7 + 56*x^6 + 106*x^5 + 100*x^4 + 93*x^3 + 24*x^2 + 125*x + 30, x^75 + 41*x^73 + 106*x^72 + 2*x^71 + 104*x^70 + 90*x^69 + 12*x^68 + 101*x^67 + 72*x^66 + 101*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 66*x^7 + 104*x^6 + 26*x^5 + 12*x^4 + 13*x^3 + 72*x^2 + 77*x + 58, x^75 + 41*x^73 + 18*x^72 + 114*x^71 + 104*x^70 + 42*x^69 + 60*x^68 + 117*x^67 + 72*x^66 + 21*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 50*x^7 + 104*x^6 + 106*x^5 + 60*x^4 + 29*x^3 + 72*x^2 + 125*x + 98, x^75 + 41*x^73 + 114*x^72 + 34*x^71 + 56*x^70 + 26*x^69 + 76*x^68 + 5*x^67 + 56*x^66 + 101*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 98*x^7 + 56*x^6 + 90*x^5 + 76*x^4 + 45*x^3 + 56*x^2 + 77*x + 50, x^75 + 41*x^73 + 66*x^72 + 18*x^71 + 40*x^70 + 74*x^69 + 92*x^68 + 85*x^67 + 8*x^66 + 117*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 82*x^7 + 40*x^6 + 10*x^5 + 92*x^4 + 125*x^3 + 8*x^2 + 93*x + 18, x^75 + 41*x^73 + 6*x^72 + 114*x^71 + 8*x^70 + 74*x^69 + 4*x^68 + 53*x^67 + 8*x^66 + 53*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 50*x^7 + 8*x^6 + 10*x^5 + 4*x^4 + 93*x^3 + 8*x^2 + 29*x + 6, x^75 + 41*x^73 + 42*x^72 + 98*x^71 + 72*x^70 + 58*x^69 + 108*x^68 + 5*x^67 + 104*x^66 + 5*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 34*x^7 + 72*x^6 + 122*x^5 + 108*x^4 + 45*x^3 + 104*x^2 + 109*x + 26, x^75 + 41*x^73 + 122*x^72 + 34*x^71 + 72*x^70 + 58*x^69 + 76*x^68 + 69*x^67 + 104*x^66 + 5*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 98*x^7 + 72*x^6 + 122*x^5 + 76*x^4 + 109*x^3 + 104*x^2 + 109*x + 106, x^75 + 41*x^73 + 126*x^72 + 82*x^71 + 88*x^70 + 74*x^69 + 100*x^68 + 21*x^67 + 120*x^66 + 117*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 18*x^7 + 88*x^6 + 10*x^5 + 100*x^4 + 61*x^3 + 120*x^2 + 93*x + 110, x^75 + 41*x^73 + 102*x^72 + 50*x^71 + 8*x^70 + 10*x^69 + 68*x^68 + 117*x^67 + 8*x^66 + 117*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 114*x^7 + 8*x^6 + 74*x^5 + 68*x^4 + 29*x^3 + 8*x^2 + 93*x + 102, x^75 + 41*x^73 + 106*x^72 + 50*x^71 + 88*x^70 + 10*x^69 + 60*x^68 + 117*x^67 + 24*x^66 + 117*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 114*x^7 + 88*x^6 + 74*x^5 + 60*x^4 + 29*x^3 + 24*x^2 + 93*x + 74, x^75 + 41*x^73 + 98*x^72 + 2*x^71 + 88*x^70 + 58*x^69 + 12*x^68 + 37*x^67 + 24*x^66 + 69*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 66*x^7 + 88*x^6 + 122*x^5 + 12*x^4 + 77*x^3 + 24*x^2 + 45*x + 2, x^75 + 41*x^73 + 10*x^72 + 82*x^71 + 120*x^70 + 106*x^69 + 92*x^68 + 85*x^67 + 120*x^66 + 21*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 18*x^7 + 120*x^6 + 42*x^5 + 92*x^4 + 125*x^3 + 120*x^2 + 125*x + 10, x^75 + 41*x^73 + 46*x^72 + 18*x^71 + 56*x^70 + 10*x^69 + 36*x^68 + 85*x^67 + 24*x^66 + 53*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 82*x^7 + 56*x^6 + 74*x^5 + 36*x^4 + 125*x^3 + 24*x^2 + 29*x + 126, x^75 + 41*x^73 + 66*x^72 + 50*x^71 + 72*x^70 + 106*x^69 + 124*x^68 + 53*x^67 + 104*x^66 + 85*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 114*x^7 + 72*x^6 + 42*x^5 + 124*x^4 + 93*x^3 + 104*x^2 + 61*x + 114, x^75 + 41*x^73 + 66*x^72 + 98*x^71 + 24*x^70 + 90*x^69 + 76*x^68 + 69*x^67 + 88*x^66 + 37*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 34*x^7 + 24*x^6 + 26*x^5 + 76*x^4 + 109*x^3 + 88*x^2 + 13*x + 98, x^75 + 41*x^73 + 54*x^72 + 82*x^71 + 72*x^70 + 106*x^69 + 100*x^68 + 85*x^67 + 72*x^66 + 21*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 18*x^7 + 72*x^6 + 42*x^5 + 100*x^4 + 125*x^3 + 72*x^2 + 125*x + 118, x^75 + 41*x^73 + 78*x^72 + 66*x^71 + 40*x^70 + 122*x^69 + 84*x^68 + 101*x^67 + 104*x^66 + 5*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 2*x^7 + 40*x^6 + 58*x^5 + 84*x^4 + 13*x^3 + 104*x^2 + 109*x + 110, x^75 + 41*x^73 + 66*x^72 + 82*x^71 + 8*x^70 + 10*x^69 + 60*x^68 + 21*x^67 + 40*x^66 + 53*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 18*x^7 + 8*x^6 + 74*x^5 + 60*x^4 + 61*x^3 + 40*x^2 + 29*x + 50, x^75 + 41*x^73 + 74*x^72 + 98*x^71 + 40*x^70 + 58*x^69 + 12*x^68 + 5*x^67 + 8*x^66 + 5*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 34*x^7 + 40*x^6 + 122*x^5 + 12*x^4 + 45*x^3 + 8*x^2 + 109*x + 90, x^75 + 41*x^73 + 102*x^72 + 18*x^71 + 8*x^70 + 42*x^69 + 4*x^68 + 21*x^67 + 8*x^66 + 85*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 82*x^7 + 8*x^6 + 106*x^5 + 4*x^4 + 61*x^3 + 8*x^2 + 61*x + 38, x^75 + 41*x^73 + 54*x^72 + 34*x^71 + 24*x^70 + 58*x^69 + 116*x^68 + 69*x^67 + 56*x^66 + 5*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 98*x^7 + 24*x^6 + 122*x^5 + 116*x^4 + 109*x^3 + 56*x^2 + 109*x + 38, x^75 + 41*x^73 + 86*x^72 + 50*x^71 + 104*x^70 + 74*x^69 + 68*x^68 + 117*x^67 + 40*x^66 + 53*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 114*x^7 + 104*x^6 + 10*x^5 + 68*x^4 + 29*x^3 + 40*x^2 + 29*x + 118, x^75 + 41*x^73 + 78*x^72 + 114*x^71 + 120*x^70 + 106*x^69 + 36*x^68 + 117*x^67 + 88*x^66 + 85*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 50*x^7 + 120*x^6 + 42*x^5 + 36*x^4 + 29*x^3 + 88*x^2 + 61*x + 94, x^75 + 41*x^73 + 86*x^72 + 82*x^71 + 72*x^70 + 106*x^69 + 36*x^68 + 85*x^67 + 72*x^66 + 21*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 18*x^7 + 72*x^6 + 42*x^5 + 36*x^4 + 125*x^3 + 72*x^2 + 125*x + 22, x^75 + 41*x^73 + 82*x^72 + 98*x^71 + 88*x^70 + 26*x^69 + 108*x^68 + 69*x^67 + 24*x^66 + 101*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 34*x^7 + 88*x^6 + 90*x^5 + 108*x^4 + 109*x^3 + 24*x^2 + 77*x + 50, x^75 + 41*x^73 + 70*x^72 + 114*x^71 + 8*x^70 + 74*x^69 + 4*x^68 + 53*x^67 + 8*x^66 + 53*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 50*x^7 + 8*x^6 + 10*x^5 + 4*x^4 + 93*x^3 + 8*x^2 + 29*x + 70, x^75 + 41*x^73 + 106*x^72 + 98*x^71 + 40*x^70 + 58*x^69 + 76*x^68 + 5*x^67 + 8*x^66 + 5*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 34*x^7 + 40*x^6 + 122*x^5 + 76*x^4 + 45*x^3 + 8*x^2 + 109*x + 122, x^75 + 41*x^73 + 58*x^72 + 98*x^71 + 8*x^70 + 122*x^69 + 12*x^68 + 5*x^67 + 40*x^66 + 69*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 34*x^7 + 8*x^6 + 58*x^5 + 12*x^4 + 45*x^3 + 40*x^2 + 45*x + 106, x^75 + 41*x^73 + 22*x^72 + 114*x^71 + 8*x^70 + 74*x^69 + 36*x^68 + 53*x^67 + 8*x^66 + 53*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 50*x^7 + 8*x^6 + 10*x^5 + 36*x^4 + 93*x^3 + 8*x^2 + 29*x + 86, x^75 + 41*x^73 + 70*x^72 + 50*x^71 + 8*x^70 + 10*x^69 + 4*x^68 + 117*x^67 + 8*x^66 + 117*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 114*x^7 + 8*x^6 + 74*x^5 + 4*x^4 + 29*x^3 + 8*x^2 + 93*x + 70, x^75 + 41*x^73 + 58*x^72 + 50*x^71 + 120*x^70 + 10*x^69 + 124*x^68 + 117*x^67 + 120*x^66 + 117*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 114*x^7 + 120*x^6 + 74*x^5 + 124*x^4 + 29*x^3 + 120*x^2 + 93*x + 58, x^75 + 41*x^73 + 114*x^72 + 82*x^71 + 8*x^70 + 10*x^69 + 28*x^68 + 21*x^67 + 40*x^66 + 53*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 18*x^7 + 8*x^6 + 74*x^5 + 28*x^4 + 61*x^3 + 40*x^2 + 29*x + 34, x^75 + 41*x^73 + 62*x^72 + 18*x^71 + 88*x^70 + 10*x^69 + 100*x^68 + 85*x^67 + 120*x^66 + 53*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 82*x^7 + 88*x^6 + 74*x^5 + 100*x^4 + 125*x^3 + 120*x^2 + 29*x + 46, x^75 + 41*x^73 + 38*x^72 + 50*x^71 + 104*x^70 + 74*x^69 + 100*x^68 + 117*x^67 + 40*x^66 + 53*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 114*x^7 + 104*x^6 + 10*x^5 + 100*x^4 + 29*x^3 + 40*x^2 + 29*x + 6, x^75 + 41*x^73 + 38*x^72 + 2*x^71 + 24*x^70 + 90*x^69 + 20*x^68 + 101*x^67 + 56*x^66 + 101*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 66*x^7 + 24*x^6 + 26*x^5 + 20*x^4 + 13*x^3 + 56*x^2 + 77*x + 22, x^75 + 41*x^73 + 2*x^72 + 18*x^71 + 8*x^70 + 74*x^69 + 60*x^68 + 85*x^67 + 40*x^66 + 117*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 82*x^7 + 8*x^6 + 10*x^5 + 60*x^4 + 125*x^3 + 40*x^2 + 93*x + 114, x^75 + 41*x^73 + 78*x^72 + 82*x^71 + 120*x^70 + 10*x^69 + 100*x^68 + 21*x^67 + 88*x^66 + 53*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 18*x^7 + 120*x^6 + 74*x^5 + 100*x^4 + 61*x^3 + 88*x^2 + 29*x + 30, x^75 + 41*x^73 + 50*x^72 + 18*x^71 + 72*x^70 + 74*x^69 + 92*x^68 + 85*x^67 + 104*x^66 + 117*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 82*x^7 + 72*x^6 + 10*x^5 + 92*x^4 + 125*x^3 + 104*x^2 + 93*x + 34, x^75 + 41*x^73 + 30*x^72 + 18*x^71 + 56*x^70 + 10*x^69 + 4*x^68 + 85*x^67 + 24*x^66 + 53*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 82*x^7 + 56*x^6 + 74*x^5 + 4*x^4 + 125*x^3 + 24*x^2 + 29*x + 46, x^75 + 41*x^73 + 78*x^72 + 50*x^71 + 88*x^70 + 42*x^69 + 4*x^68 + 53*x^67 + 120*x^66 + 21*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 114*x^7 + 88*x^6 + 106*x^5 + 4*x^4 + 93*x^3 + 120*x^2 + 125*x + 126, x^75 + 41*x^73 + 102*x^72 + 98*x^71 + 88*x^70 + 122*x^69 + 20*x^68 + 5*x^67 + 120*x^66 + 69*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 34*x^7 + 88*x^6 + 58*x^5 + 20*x^4 + 45*x^3 + 120*x^2 + 45*x + 86, x^75 + 41*x^73 + 10*x^72 + 66*x^71 + 8*x^70 + 90*x^69 + 44*x^68 + 37*x^67 + 40*x^66 + 101*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 2*x^7 + 8*x^6 + 26*x^5 + 44*x^4 + 77*x^3 + 40*x^2 + 77*x + 122, x^75 + 41*x^73 + 74*x^72 + 66*x^71 + 104*x^70 + 26*x^69 + 76*x^68 + 37*x^67 + 72*x^66 + 37*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 2*x^7 + 104*x^6 + 90*x^5 + 76*x^4 + 77*x^3 + 72*x^2 + 13*x + 26, x^75 + 41*x^73 + 46*x^72 + 2*x^71 + 40*x^70 + 122*x^69 + 84*x^68 + 37*x^67 + 104*x^66 + 5*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 66*x^7 + 40*x^6 + 58*x^5 + 84*x^4 + 77*x^3 + 104*x^2 + 109*x + 14, x^75 + 41*x^73 + 126*x^72 + 66*x^71 + 8*x^70 + 122*x^69 + 20*x^68 + 101*x^67 + 8*x^66 + 5*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 2*x^7 + 8*x^6 + 58*x^5 + 20*x^4 + 13*x^3 + 8*x^2 + 109*x + 126, x^75 + 41*x^73 + 94*x^72 + 114*x^71 + 56*x^70 + 42*x^69 + 68*x^68 + 117*x^67 + 24*x^66 + 21*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 50*x^7 + 56*x^6 + 106*x^5 + 68*x^4 + 29*x^3 + 24*x^2 + 125*x + 46, x^75 + 41*x^73 + 50*x^72 + 98*x^71 + 120*x^70 + 26*x^69 + 76*x^68 + 69*x^67 + 120*x^66 + 101*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 34*x^7 + 120*x^6 + 90*x^5 + 76*x^4 + 109*x^3 + 120*x^2 + 77*x + 114, x^75 + 41*x^73 + 38*x^72 + 82*x^71 + 40*x^70 + 42*x^69 + 100*x^68 + 85*x^67 + 104*x^66 + 85*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 18*x^7 + 40*x^6 + 106*x^5 + 100*x^4 + 125*x^3 + 104*x^2 + 61*x + 6, x^75 + 41*x^73 + 42*x^72 + 114*x^71 + 88*x^70 + 74*x^69 + 60*x^68 + 53*x^67 + 24*x^66 + 53*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 50*x^7 + 88*x^6 + 10*x^5 + 60*x^4 + 93*x^3 + 24*x^2 + 29*x + 10, x^75 + 41*x^73 + 86*x^72 + 2*x^71 + 88*x^70 + 26*x^69 + 116*x^68 + 101*x^67 + 120*x^66 + 37*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 66*x^7 + 88*x^6 + 90*x^5 + 116*x^4 + 13*x^3 + 120*x^2 + 13*x + 6, x^75 + 41*x^73 + 94*x^72 + 50*x^71 + 56*x^70 + 106*x^69 + 68*x^68 + 53*x^67 + 24*x^66 + 85*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 114*x^7 + 56*x^6 + 42*x^5 + 68*x^4 + 93*x^3 + 24*x^2 + 61*x + 46, x^75 + 41*x^73 + 82*x^72 + 114*x^71 + 8*x^70 + 106*x^69 + 28*x^68 + 117*x^67 + 40*x^66 + 85*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 50*x^7 + 8*x^6 + 42*x^5 + 28*x^4 + 29*x^3 + 40*x^2 + 61*x + 66, x^75 + 41*x^73 + 114*x^72 + 66*x^71 + 88*x^70 + 58*x^69 + 108*x^68 + 101*x^67 + 24*x^66 + 69*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 2*x^7 + 88*x^6 + 122*x^5 + 108*x^4 + 13*x^3 + 24*x^2 + 45*x + 18, x^75 + 41*x^73 + 86*x^72 + 2*x^71 + 120*x^70 + 26*x^69 + 20*x^68 + 101*x^67 + 88*x^66 + 37*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 66*x^7 + 120*x^6 + 90*x^5 + 20*x^4 + 13*x^3 + 88*x^2 + 13*x + 102, x^75 + 41*x^73 + 30*x^72 + 18*x^71 + 120*x^70 + 74*x^69 + 4*x^68 + 85*x^67 + 88*x^66 + 117*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 82*x^7 + 120*x^6 + 10*x^5 + 4*x^4 + 125*x^3 + 88*x^2 + 93*x + 46, x^75 + 41*x^73 + 18*x^72 + 114*x^71 + 40*x^70 + 106*x^69 + 60*x^68 + 117*x^67 + 8*x^66 + 85*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 50*x^7 + 40*x^6 + 42*x^5 + 60*x^4 + 29*x^3 + 8*x^2 + 61*x + 98, x^75 + 41*x^73 + 54*x^72 + 114*x^71 + 104*x^70 + 10*x^69 + 4*x^68 + 53*x^67 + 40*x^66 + 117*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 50*x^7 + 104*x^6 + 74*x^5 + 4*x^4 + 93*x^3 + 40*x^2 + 93*x + 86, x^75 + 41*x^73 + 78*x^72 + 98*x^71 + 72*x^70 + 26*x^69 + 116*x^68 + 69*x^67 + 72*x^66 + 101*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 34*x^7 + 72*x^6 + 90*x^5 + 116*x^4 + 109*x^3 + 72*x^2 + 77*x + 78, x^75 + 41*x^73 + 42*x^72 + 34*x^71 + 104*x^70 + 58*x^69 + 76*x^68 + 69*x^67 + 72*x^66 + 5*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 98*x^7 + 104*x^6 + 122*x^5 + 76*x^4 + 109*x^3 + 72*x^2 + 109*x + 58, x^75 + 41*x^73 + 82*x^72 + 34*x^71 + 120*x^70 + 26*x^69 + 76*x^68 + 5*x^67 + 120*x^66 + 101*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 98*x^7 + 120*x^6 + 90*x^5 + 76*x^4 + 45*x^3 + 120*x^2 + 77*x + 82, x^75 + 41*x^73 + 118*x^72 + 50*x^71 + 72*x^70 + 74*x^69 + 100*x^68 + 117*x^67 + 72*x^66 + 53*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 114*x^7 + 72*x^6 + 10*x^5 + 100*x^4 + 29*x^3 + 72*x^2 + 29*x + 54, x^75 + 41*x^73 + 58*x^72 + 34*x^71 + 8*x^70 + 122*x^69 + 76*x^68 + 69*x^67 + 40*x^66 + 69*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 98*x^7 + 8*x^6 + 58*x^5 + 76*x^4 + 109*x^3 + 40*x^2 + 45*x + 42, x^75 + 41*x^73 + 86*x^72 + 98*x^71 + 120*x^70 + 58*x^69 + 84*x^68 + 5*x^67 + 88*x^66 + 5*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 34*x^7 + 120*x^6 + 122*x^5 + 84*x^4 + 45*x^3 + 88*x^2 + 109*x + 38, x^75 + 41*x^73 + 82*x^72 + 34*x^71 + 24*x^70 + 26*x^69 + 108*x^68 + 5*x^67 + 88*x^66 + 101*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 98*x^7 + 24*x^6 + 90*x^5 + 108*x^4 + 45*x^3 + 88*x^2 + 77*x + 50, x^75 + 41*x^73 + 50*x^72 + 98*x^71 + 24*x^70 + 26*x^69 + 108*x^68 + 69*x^67 + 88*x^66 + 101*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 34*x^7 + 24*x^6 + 90*x^5 + 108*x^4 + 109*x^3 + 88*x^2 + 77*x + 82, x^75 + 41*x^73 + 90*x^72 + 2*x^71 + 8*x^70 + 90*x^69 + 12*x^68 + 101*x^67 + 40*x^66 + 101*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 66*x^7 + 8*x^6 + 26*x^5 + 12*x^4 + 13*x^3 + 40*x^2 + 77*x + 74, x^75 + 41*x^73 + 78*x^72 + 2*x^71 + 8*x^70 + 122*x^69 + 116*x^68 + 37*x^67 + 8*x^66 + 5*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 66*x^7 + 8*x^6 + 58*x^5 + 116*x^4 + 77*x^3 + 8*x^2 + 109*x + 78, x^75 + 41*x^73 + 2*x^72 + 50*x^71 + 72*x^70 + 42*x^69 + 60*x^68 + 53*x^67 + 104*x^66 + 21*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 114*x^7 + 72*x^6 + 106*x^5 + 60*x^4 + 93*x^3 + 104*x^2 + 125*x + 114, x^75 + 41*x^73 + 122*x^72 + 50*x^71 + 24*x^70 + 10*x^69 + 28*x^68 + 117*x^67 + 88*x^66 + 117*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 114*x^7 + 24*x^6 + 74*x^5 + 28*x^4 + 29*x^3 + 88*x^2 + 93*x + 90, x^75 + 41*x^73 + 122*x^72 + 2*x^71 + 8*x^70 + 26*x^69 + 12*x^68 + 101*x^67 + 40*x^66 + 37*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 66*x^7 + 8*x^6 + 90*x^5 + 12*x^4 + 13*x^3 + 40*x^2 + 13*x + 42, x^75 + 41*x^73 + 74*x^72 + 66*x^71 + 104*x^70 + 90*x^69 + 12*x^68 + 37*x^67 + 72*x^66 + 101*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 2*x^7 + 104*x^6 + 26*x^5 + 12*x^4 + 77*x^3 + 72*x^2 + 77*x + 90, x^75 + 41*x^73 + 90*x^72 + 82*x^71 + 120*x^70 + 106*x^69 + 124*x^68 + 85*x^67 + 120*x^66 + 21*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 18*x^7 + 120*x^6 + 42*x^5 + 124*x^4 + 125*x^3 + 120*x^2 + 125*x + 26, x^75 + 41*x^73 + 82*x^72 + 50*x^71 + 104*x^70 + 106*x^69 + 60*x^68 + 53*x^67 + 72*x^66 + 85*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 114*x^7 + 104*x^6 + 42*x^5 + 60*x^4 + 93*x^3 + 72*x^2 + 61*x + 34, x^75 + 41*x^73 + 82*x^72 + 82*x^71 + 72*x^70 + 74*x^69 + 92*x^68 + 21*x^67 + 104*x^66 + 117*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 18*x^7 + 72*x^6 + 10*x^5 + 92*x^4 + 61*x^3 + 104*x^2 + 93*x + 2, x^75 + 41*x^73 + 10*x^72 + 18*x^71 + 24*x^70 + 106*x^69 + 60*x^68 + 21*x^67 + 88*x^66 + 21*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 82*x^7 + 24*x^6 + 42*x^5 + 60*x^4 + 61*x^3 + 88*x^2 + 125*x + 42, x^75 + 41*x^73 + 118*x^72 + 66*x^71 + 88*x^70 + 26*x^69 + 116*x^68 + 37*x^67 + 120*x^66 + 37*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 2*x^7 + 88*x^6 + 90*x^5 + 116*x^4 + 77*x^3 + 120*x^2 + 13*x + 102, x^75 + 41*x^73 + 78*x^72 + 66*x^71 + 72*x^70 + 58*x^69 + 52*x^68 + 101*x^67 + 72*x^66 + 69*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 2*x^7 + 72*x^6 + 122*x^5 + 52*x^4 + 13*x^3 + 72*x^2 + 45*x + 14, x^75 + 41*x^73 + 58*x^72 + 82*x^71 + 120*x^70 + 106*x^69 + 60*x^68 + 85*x^67 + 120*x^66 + 21*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 18*x^7 + 120*x^6 + 42*x^5 + 60*x^4 + 125*x^3 + 120*x^2 + 125*x + 122, x^75 + 41*x^73 + 126*x^72 + 34*x^71 + 40*x^70 + 90*x^69 + 52*x^68 + 5*x^67 + 104*x^66 + 37*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 98*x^7 + 40*x^6 + 26*x^5 + 52*x^4 + 45*x^3 + 104*x^2 + 13*x + 94, x^75 + 41*x^73 + 38*x^72 + 66*x^71 + 24*x^70 + 26*x^69 + 20*x^68 + 37*x^67 + 56*x^66 + 37*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 2*x^7 + 24*x^6 + 90*x^5 + 20*x^4 + 77*x^3 + 56*x^2 + 13*x + 22, x^75 + 41*x^73 + 98*x^72 + 98*x^71 + 88*x^70 + 90*x^69 + 76*x^68 + 69*x^67 + 24*x^66 + 37*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 34*x^7 + 88*x^6 + 26*x^5 + 76*x^4 + 109*x^3 + 24*x^2 + 13*x + 66, x^75 + 41*x^73 + 122*x^72 + 82*x^71 + 88*x^70 + 106*x^69 + 28*x^68 + 85*x^67 + 24*x^66 + 21*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 18*x^7 + 88*x^6 + 42*x^5 + 28*x^4 + 125*x^3 + 24*x^2 + 125*x + 90, x^75 + 41*x^73 + 34*x^72 + 66*x^71 + 24*x^70 + 122*x^69 + 76*x^68 + 101*x^67 + 88*x^66 + 5*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 2*x^7 + 24*x^6 + 58*x^5 + 76*x^4 + 13*x^3 + 88*x^2 + 109*x + 2, x^75 + 41*x^73 + 30*x^72 + 82*x^71 + 24*x^70 + 10*x^69 + 36*x^68 + 21*x^67 + 56*x^66 + 53*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 18*x^7 + 24*x^6 + 74*x^5 + 36*x^4 + 61*x^3 + 56*x^2 + 29*x + 14, x^75 + 41*x^73 + 66*x^72 + 2*x^71 + 120*x^70 + 122*x^69 + 44*x^68 + 37*x^67 + 120*x^66 + 5*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 66*x^7 + 120*x^6 + 58*x^5 + 44*x^4 + 77*x^3 + 120*x^2 + 109*x + 2, x^75 + 41*x^73 + 22*x^72 + 66*x^71 + 120*x^70 + 90*x^69 + 20*x^68 + 37*x^67 + 88*x^66 + 101*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 2*x^7 + 120*x^6 + 26*x^5 + 20*x^4 + 77*x^3 + 88*x^2 + 77*x + 38, x^75 + 41*x^73 + 110*x^72 + 2*x^71 + 72*x^70 + 58*x^69 + 52*x^68 + 37*x^67 + 72*x^66 + 69*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 66*x^7 + 72*x^6 + 122*x^5 + 52*x^4 + 77*x^3 + 72*x^2 + 45*x + 110, x^75 + 41*x^73 + 26*x^72 + 82*x^71 + 88*x^70 + 106*x^69 + 92*x^68 + 85*x^67 + 24*x^66 + 21*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 18*x^7 + 88*x^6 + 42*x^5 + 92*x^4 + 125*x^3 + 24*x^2 + 125*x + 122, x^75 + 41*x^73 + 42*x^72 + 82*x^71 + 88*x^70 + 106*x^69 + 124*x^68 + 85*x^67 + 24*x^66 + 21*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 18*x^7 + 88*x^6 + 42*x^5 + 124*x^4 + 125*x^3 + 24*x^2 + 125*x + 74, x^75 + 41*x^73 + 118*x^72 + 98*x^71 + 56*x^70 + 58*x^69 + 84*x^68 + 5*x^67 + 24*x^66 + 5*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 34*x^7 + 56*x^6 + 122*x^5 + 84*x^4 + 45*x^3 + 24*x^2 + 109*x + 6, x^75 + 41*x^73 + 30*x^72 + 50*x^71 + 88*x^70 + 106*x^69 + 100*x^68 + 53*x^67 + 120*x^66 + 85*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 114*x^7 + 88*x^6 + 42*x^5 + 100*x^4 + 93*x^3 + 120*x^2 + 61*x + 78, x^75 + 41*x^73 + 10*x^72 + 50*x^71 + 120*x^70 + 10*x^69 + 28*x^68 + 117*x^67 + 120*x^66 + 117*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 114*x^7 + 120*x^6 + 74*x^5 + 28*x^4 + 29*x^3 + 120*x^2 + 93*x + 74, x^75 + 41*x^73 + 6*x^72 + 18*x^71 + 40*x^70 + 42*x^69 + 100*x^68 + 21*x^67 + 104*x^66 + 85*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 82*x^7 + 40*x^6 + 106*x^5 + 100*x^4 + 61*x^3 + 104*x^2 + 61*x + 38, x^75 + 41*x^73 + 10*x^72 + 2*x^71 + 8*x^70 + 26*x^69 + 44*x^68 + 101*x^67 + 40*x^66 + 37*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 66*x^7 + 8*x^6 + 90*x^5 + 44*x^4 + 13*x^3 + 40*x^2 + 13*x + 122, x^75 + 41*x^73 + 18*x^72 + 98*x^71 + 88*x^70 + 26*x^69 + 108*x^68 + 69*x^67 + 24*x^66 + 101*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 34*x^7 + 88*x^6 + 90*x^5 + 108*x^4 + 109*x^3 + 24*x^2 + 77*x + 114, x^75 + 41*x^73 + 70*x^72 + 114*x^71 + 40*x^70 + 10*x^69 + 100*x^68 + 53*x^67 + 104*x^66 + 117*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 50*x^7 + 40*x^6 + 74*x^5 + 100*x^4 + 93*x^3 + 104*x^2 + 93*x + 102, x^75 + 41*x^73 + 74*x^72 + 50*x^71 + 88*x^70 + 74*x^69 + 60*x^68 + 117*x^67 + 24*x^66 + 53*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 114*x^7 + 88*x^6 + 10*x^5 + 60*x^4 + 29*x^3 + 24*x^2 + 29*x + 106, x^75 + 41*x^73 + 102*x^72 + 66*x^71 + 24*x^70 + 26*x^69 + 20*x^68 + 37*x^67 + 56*x^66 + 37*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 2*x^7 + 24*x^6 + 90*x^5 + 20*x^4 + 77*x^3 + 56*x^2 + 13*x + 86, x^75 + 41*x^73 + 14*x^72 + 18*x^71 + 24*x^70 + 74*x^69 + 4*x^68 + 85*x^67 + 56*x^66 + 117*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 82*x^7 + 24*x^6 + 10*x^5 + 4*x^4 + 125*x^3 + 56*x^2 + 93*x + 62, x^75 + 41*x^73 + 90*x^72 + 82*x^71 + 88*x^70 + 42*x^69 + 28*x^68 + 85*x^67 + 24*x^66 + 85*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 18*x^7 + 88*x^6 + 106*x^5 + 28*x^4 + 125*x^3 + 24*x^2 + 61*x + 122, x^75 + 41*x^73 + 82*x^72 + 2*x^71 + 88*x^70 + 122*x^69 + 44*x^68 + 37*x^67 + 24*x^66 + 5*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 66*x^7 + 88*x^6 + 58*x^5 + 44*x^4 + 77*x^3 + 24*x^2 + 109*x + 114, x^75 + 41*x^73 + 30*x^72 + 82*x^71 + 88*x^70 + 74*x^69 + 36*x^68 + 21*x^67 + 120*x^66 + 117*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 18*x^7 + 88*x^6 + 10*x^5 + 36*x^4 + 61*x^3 + 120*x^2 + 93*x + 14, x^75 + 41*x^73 + 2*x^72 + 18*x^71 + 72*x^70 + 10*x^69 + 60*x^68 + 85*x^67 + 104*x^66 + 53*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 82*x^7 + 72*x^6 + 74*x^5 + 60*x^4 + 125*x^3 + 104*x^2 + 29*x + 114, x^75 + 41*x^73 + 118*x^72 + 114*x^71 + 72*x^70 + 10*x^69 + 100*x^68 + 53*x^67 + 72*x^66 + 117*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 50*x^7 + 72*x^6 + 74*x^5 + 100*x^4 + 93*x^3 + 72*x^2 + 93*x + 54, x^75 + 41*x^73 + 54*x^72 + 98*x^71 + 88*x^70 + 122*x^69 + 52*x^68 + 5*x^67 + 120*x^66 + 69*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 34*x^7 + 88*x^6 + 58*x^5 + 52*x^4 + 45*x^3 + 120*x^2 + 45*x + 102, x^75 + 41*x^73 + 14*x^72 + 66*x^71 + 72*x^70 + 58*x^69 + 52*x^68 + 101*x^67 + 72*x^66 + 69*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 2*x^7 + 72*x^6 + 122*x^5 + 52*x^4 + 13*x^3 + 72*x^2 + 45*x + 78, x^75 + 41*x^73 + 122*x^72 + 98*x^71 + 8*x^70 + 58*x^69 + 76*x^68 + 5*x^67 + 40*x^66 + 5*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 34*x^7 + 8*x^6 + 122*x^5 + 76*x^4 + 45*x^3 + 40*x^2 + 109*x + 106, x^75 + 41*x^73 + 106*x^72 + 66*x^71 + 8*x^70 + 26*x^69 + 44*x^68 + 37*x^67 + 40*x^66 + 37*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 2*x^7 + 8*x^6 + 90*x^5 + 44*x^4 + 77*x^3 + 40*x^2 + 13*x + 26, x^75 + 41*x^73 + 58*x^72 + 2*x^71 + 104*x^70 + 90*x^69 + 44*x^68 + 101*x^67 + 72*x^66 + 101*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 66*x^7 + 104*x^6 + 26*x^5 + 44*x^4 + 13*x^3 + 72*x^2 + 77*x + 74, x^75 + 41*x^73 + 14*x^72 + 50*x^71 + 120*x^70 + 42*x^69 + 36*x^68 + 53*x^67 + 88*x^66 + 21*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 114*x^7 + 120*x^6 + 106*x^5 + 36*x^4 + 93*x^3 + 88*x^2 + 125*x + 30, x^75 + 41*x^73 + 70*x^72 + 66*x^71 + 120*x^70 + 90*x^69 + 116*x^68 + 37*x^67 + 88*x^66 + 101*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 2*x^7 + 120*x^6 + 26*x^5 + 116*x^4 + 77*x^3 + 88*x^2 + 77*x + 22, x^75 + 41*x^73 + 106*x^72 + 50*x^71 + 120*x^70 + 74*x^69 + 28*x^68 + 117*x^67 + 120*x^66 + 53*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 114*x^7 + 120*x^6 + 10*x^5 + 28*x^4 + 29*x^3 + 120*x^2 + 29*x + 106, x^75 + 41*x^73 + 82*x^72 + 66*x^71 + 120*x^70 + 58*x^69 + 76*x^68 + 101*x^67 + 120*x^66 + 69*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 2*x^7 + 120*x^6 + 122*x^5 + 76*x^4 + 13*x^3 + 120*x^2 + 45*x + 82, x^75 + 41*x^73 + 18*x^72 + 18*x^71 + 8*x^70 + 10*x^69 + 28*x^68 + 85*x^67 + 40*x^66 + 53*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 82*x^7 + 8*x^6 + 74*x^5 + 28*x^4 + 125*x^3 + 40*x^2 + 29*x + 2, x^75 + 41*x^73 + 118*x^72 + 66*x^71 + 56*x^70 + 90*x^69 + 20*x^68 + 37*x^67 + 24*x^66 + 101*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 2*x^7 + 56*x^6 + 26*x^5 + 20*x^4 + 77*x^3 + 24*x^2 + 77*x + 70, x^75 + 41*x^73 + 2*x^72 + 98*x^71 + 56*x^70 + 90*x^69 + 108*x^68 + 69*x^67 + 56*x^66 + 37*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 34*x^7 + 56*x^6 + 26*x^5 + 108*x^4 + 109*x^3 + 56*x^2 + 13*x + 2, x^75 + 41*x^73 + 102*x^72 + 98*x^71 + 88*x^70 + 58*x^69 + 84*x^68 + 5*x^67 + 120*x^66 + 5*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 34*x^7 + 88*x^6 + 122*x^5 + 84*x^4 + 45*x^3 + 120*x^2 + 109*x + 22, x^75 + 41*x^73 + 110*x^72 + 50*x^71 + 120*x^70 + 42*x^69 + 100*x^68 + 53*x^67 + 88*x^66 + 21*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 114*x^7 + 120*x^6 + 106*x^5 + 100*x^4 + 93*x^3 + 88*x^2 + 125*x + 126, x^75 + 41*x^73 + 106*x^72 + 66*x^71 + 104*x^70 + 90*x^69 + 76*x^68 + 37*x^67 + 72*x^66 + 101*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 2*x^7 + 104*x^6 + 26*x^5 + 76*x^4 + 77*x^3 + 72*x^2 + 77*x + 122, x^75 + 41*x^73 + 118*x^72 + 18*x^71 + 40*x^70 + 106*x^69 + 4*x^68 + 21*x^67 + 104*x^66 + 21*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 82*x^7 + 40*x^6 + 42*x^5 + 4*x^4 + 61*x^3 + 104*x^2 + 125*x + 22, x^75 + 41*x^73 + 82*x^72 + 34*x^71 + 120*x^70 + 90*x^69 + 12*x^68 + 5*x^67 + 120*x^66 + 37*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 98*x^7 + 120*x^6 + 26*x^5 + 12*x^4 + 45*x^3 + 120*x^2 + 13*x + 18, x^75 + 41*x^73 + 94*x^72 + 114*x^71 + 120*x^70 + 106*x^69 + 68*x^68 + 117*x^67 + 88*x^66 + 85*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 50*x^7 + 120*x^6 + 42*x^5 + 68*x^4 + 29*x^3 + 88*x^2 + 61*x + 46, x^75 + 41*x^73 + 14*x^72 + 82*x^71 + 120*x^70 + 10*x^69 + 100*x^68 + 21*x^67 + 88*x^66 + 53*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 18*x^7 + 120*x^6 + 74*x^5 + 100*x^4 + 61*x^3 + 88*x^2 + 29*x + 94, x^75 + 41*x^73 + 102*x^72 + 50*x^71 + 104*x^70 + 74*x^69 + 100*x^68 + 117*x^67 + 40*x^66 + 53*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 114*x^7 + 104*x^6 + 10*x^5 + 100*x^4 + 29*x^3 + 40*x^2 + 29*x + 70, x^75 + 41*x^73 + 34*x^72 + 2*x^71 + 56*x^70 + 122*x^69 + 44*x^68 + 37*x^67 + 56*x^66 + 5*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 66*x^7 + 56*x^6 + 58*x^5 + 44*x^4 + 77*x^3 + 56*x^2 + 109*x + 34, x^75 + 41*x^73 + 10*x^72 + 114*x^71 + 24*x^70 + 10*x^69 + 124*x^68 + 53*x^67 + 88*x^66 + 117*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 50*x^7 + 24*x^6 + 74*x^5 + 124*x^4 + 93*x^3 + 88*x^2 + 93*x + 106, x^75 + 41*x^73 + 42*x^72 + 18*x^71 + 88*x^70 + 42*x^69 + 124*x^68 + 21*x^67 + 24*x^66 + 85*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 82*x^7 + 88*x^6 + 106*x^5 + 124*x^4 + 61*x^3 + 24*x^2 + 61*x + 74, x^75 + 41*x^73 + 98*x^72 + 18*x^71 + 72*x^70 + 74*x^69 + 60*x^68 + 85*x^67 + 104*x^66 + 117*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 82*x^7 + 72*x^6 + 10*x^5 + 60*x^4 + 125*x^3 + 104*x^2 + 93*x + 18, x^75 + 41*x^73 + 110*x^72 + 2*x^71 + 40*x^70 + 122*x^69 + 84*x^68 + 37*x^67 + 104*x^66 + 5*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 66*x^7 + 40*x^6 + 58*x^5 + 84*x^4 + 77*x^3 + 104*x^2 + 109*x + 78, x^75 + 41*x^73 + 30*x^72 + 34*x^71 + 40*x^70 + 26*x^69 + 52*x^68 + 5*x^67 + 104*x^66 + 101*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 98*x^7 + 40*x^6 + 90*x^5 + 52*x^4 + 45*x^3 + 104*x^2 + 77*x + 62, x^75 + 41*x^73 + 30*x^72 + 34*x^71 + 104*x^70 + 26*x^69 + 116*x^68 + 5*x^67 + 40*x^66 + 101*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 98*x^7 + 104*x^6 + 90*x^5 + 116*x^4 + 45*x^3 + 40*x^2 + 77*x + 126, x^75 + 41*x^73 + 126*x^72 + 114*x^71 + 120*x^70 + 106*x^69 + 4*x^68 + 117*x^67 + 88*x^66 + 85*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 50*x^7 + 120*x^6 + 42*x^5 + 4*x^4 + 29*x^3 + 88*x^2 + 61*x + 78, x^75 + 41*x^73 + 2*x^72 + 114*x^71 + 104*x^70 + 106*x^69 + 92*x^68 + 117*x^67 + 72*x^66 + 85*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 50*x^7 + 104*x^6 + 42*x^5 + 92*x^4 + 29*x^3 + 72*x^2 + 61*x + 82, x^75 + 41*x^73 + 126*x^72 + 18*x^71 + 24*x^70 + 10*x^69 + 36*x^68 + 85*x^67 + 56*x^66 + 53*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 82*x^7 + 24*x^6 + 74*x^5 + 36*x^4 + 125*x^3 + 56*x^2 + 29*x + 46, x^75 + 41*x^73 + 10*x^72 + 2*x^71 + 40*x^70 + 26*x^69 + 76*x^68 + 101*x^67 + 8*x^66 + 37*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 66*x^7 + 40*x^6 + 90*x^5 + 76*x^4 + 13*x^3 + 8*x^2 + 13*x + 90, x^75 + 41*x^73 + 22*x^72 + 66*x^71 + 88*x^70 + 90*x^69 + 116*x^68 + 37*x^67 + 120*x^66 + 101*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 2*x^7 + 88*x^6 + 26*x^5 + 116*x^4 + 77*x^3 + 120*x^2 + 77*x + 70, x^75 + 41*x^73 + 94*x^72 + 34*x^71 + 40*x^70 + 26*x^69 + 52*x^68 + 5*x^67 + 104*x^66 + 101*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 98*x^7 + 40*x^6 + 90*x^5 + 52*x^4 + 45*x^3 + 104*x^2 + 77*x + 126, x^75 + 41*x^73 + 50*x^72 + 18*x^71 + 72*x^70 + 10*x^69 + 28*x^68 + 85*x^67 + 104*x^66 + 53*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 82*x^7 + 72*x^6 + 74*x^5 + 28*x^4 + 125*x^3 + 104*x^2 + 29*x + 98, x^75 + 41*x^73 + 126*x^72 + 114*x^71 + 56*x^70 + 106*x^69 + 68*x^68 + 117*x^67 + 24*x^66 + 85*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 50*x^7 + 56*x^6 + 42*x^5 + 68*x^4 + 29*x^3 + 24*x^2 + 61*x + 14, x^75 + 41*x^73 + 62*x^72 + 114*x^71 + 120*x^70 + 106*x^69 + 4*x^68 + 117*x^67 + 88*x^66 + 85*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 50*x^7 + 120*x^6 + 42*x^5 + 4*x^4 + 29*x^3 + 88*x^2 + 61*x + 14, x^75 + 41*x^73 + 66*x^72 + 98*x^71 + 88*x^70 + 26*x^69 + 76*x^68 + 69*x^67 + 24*x^66 + 101*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 34*x^7 + 88*x^6 + 90*x^5 + 76*x^4 + 109*x^3 + 24*x^2 + 77*x + 98, x^75 + 41*x^73 + 46*x^72 + 50*x^71 + 24*x^70 + 42*x^69 + 4*x^68 + 53*x^67 + 56*x^66 + 21*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 114*x^7 + 24*x^6 + 106*x^5 + 4*x^4 + 93*x^3 + 56*x^2 + 125*x + 30, x^75 + 41*x^73 + 82*x^72 + 34*x^71 + 56*x^70 + 26*x^69 + 12*x^68 + 5*x^67 + 56*x^66 + 101*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 98*x^7 + 56*x^6 + 90*x^5 + 12*x^4 + 45*x^3 + 56*x^2 + 77*x + 18, x^75 + 41*x^73 + 14*x^72 + 18*x^71 + 88*x^70 + 10*x^69 + 4*x^68 + 85*x^67 + 120*x^66 + 53*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 82*x^7 + 88*x^6 + 74*x^5 + 4*x^4 + 125*x^3 + 120*x^2 + 29*x + 62, x^75 + 41*x^73 + 102*x^72 + 2*x^71 + 56*x^70 + 26*x^69 + 116*x^68 + 101*x^67 + 24*x^66 + 37*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 66*x^7 + 56*x^6 + 90*x^5 + 116*x^4 + 13*x^3 + 24*x^2 + 13*x + 118, x^75 + 41*x^73 + 118*x^72 + 34*x^71 + 120*x^70 + 58*x^69 + 84*x^68 + 69*x^67 + 88*x^66 + 5*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 98*x^7 + 120*x^6 + 122*x^5 + 84*x^4 + 109*x^3 + 88*x^2 + 109*x + 6, x^75 + 41*x^73 + 86*x^72 + 82*x^71 + 8*x^70 + 106*x^69 + 100*x^68 + 85*x^67 + 8*x^66 + 21*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 18*x^7 + 8*x^6 + 42*x^5 + 100*x^4 + 125*x^3 + 8*x^2 + 125*x + 86, x^75 + 41*x^73 + 74*x^72 + 98*x^71 + 40*x^70 + 122*x^69 + 76*x^68 + 5*x^67 + 8*x^66 + 69*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 34*x^7 + 40*x^6 + 58*x^5 + 76*x^4 + 45*x^3 + 8*x^2 + 45*x + 26, x^75 + 41*x^73 + 58*x^72 + 34*x^71 + 72*x^70 + 122*x^69 + 12*x^68 + 69*x^67 + 104*x^66 + 69*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 98*x^7 + 72*x^6 + 58*x^5 + 12*x^4 + 109*x^3 + 104*x^2 + 45*x + 106, x^75 + 41*x^73 + 6*x^72 + 18*x^71 + 8*x^70 + 106*x^69 + 4*x^68 + 21*x^67 + 8*x^66 + 21*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 82*x^7 + 8*x^6 + 42*x^5 + 4*x^4 + 61*x^3 + 8*x^2 + 125*x + 6, x^75 + 41*x^73 + 58*x^72 + 66*x^71 + 40*x^70 + 90*x^69 + 44*x^68 + 37*x^67 + 8*x^66 + 101*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 2*x^7 + 40*x^6 + 26*x^5 + 44*x^4 + 77*x^3 + 8*x^2 + 77*x + 74, x^75 + 41*x^73 + 118*x^72 + 114*x^71 + 40*x^70 + 74*x^69 + 4*x^68 + 53*x^67 + 104*x^66 + 53*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 50*x^7 + 40*x^6 + 10*x^5 + 4*x^4 + 93*x^3 + 104*x^2 + 29*x + 22, x^75 + 41*x^73 + 22*x^72 + 114*x^71 + 104*x^70 + 74*x^69 + 4*x^68 + 53*x^67 + 40*x^66 + 53*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 50*x^7 + 104*x^6 + 10*x^5 + 4*x^4 + 93*x^3 + 40*x^2 + 29*x + 118, x^75 + 41*x^73 + 18*x^72 + 82*x^71 + 72*x^70 + 74*x^69 + 92*x^68 + 21*x^67 + 104*x^66 + 117*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 18*x^7 + 72*x^6 + 10*x^5 + 92*x^4 + 61*x^3 + 104*x^2 + 93*x + 66, x^75 + 41*x^73 + 42*x^72 + 98*x^71 + 40*x^70 + 58*x^69 + 76*x^68 + 5*x^67 + 8*x^66 + 5*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 26*x^8 + 34*x^7 + 40*x^6 + 122*x^5 + 76*x^4 + 45*x^3 + 8*x^2 + 109*x + 58, x^75 + 41*x^73 + 94*x^72 + 34*x^71 + 72*x^70 + 90*x^69 + 20*x^68 + 5*x^67 + 72*x^66 + 37*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 46*x^8 + 98*x^7 + 72*x^6 + 26*x^5 + 20*x^4 + 45*x^3 + 72*x^2 + 13*x + 30, x^75 + 41*x^73 + 46*x^72 + 18*x^71 + 120*x^70 + 74*x^69 + 36*x^68 + 85*x^67 + 88*x^66 + 117*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 82*x^7 + 120*x^6 + 10*x^5 + 36*x^4 + 125*x^3 + 88*x^2 + 93*x + 126, x^75 + 41*x^73 + 18*x^72 + 50*x^71 + 8*x^70 + 106*x^69 + 92*x^68 + 53*x^67 + 40*x^66 + 85*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 114*x^7 + 8*x^6 + 42*x^5 + 92*x^4 + 93*x^3 + 40*x^2 + 61*x + 66, x^75 + 41*x^73 + 26*x^72 + 82*x^71 + 88*x^70 + 42*x^69 + 28*x^68 + 85*x^67 + 24*x^66 + 85*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 18*x^7 + 88*x^6 + 106*x^5 + 28*x^4 + 125*x^3 + 24*x^2 + 61*x + 58, x^75 + 41*x^73 + 26*x^72 + 34*x^71 + 8*x^70 + 122*x^69 + 12*x^68 + 69*x^67 + 40*x^66 + 69*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 98*x^7 + 8*x^6 + 58*x^5 + 12*x^4 + 109*x^3 + 40*x^2 + 45*x + 10, x^75 + 41*x^73 + 34*x^72 + 18*x^71 + 8*x^70 + 74*x^69 + 124*x^68 + 85*x^67 + 40*x^66 + 117*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 82*x^7 + 8*x^6 + 10*x^5 + 124*x^4 + 125*x^3 + 40*x^2 + 93*x + 18, x^75 + 41*x^73 + 14*x^72 + 98*x^71 + 104*x^70 + 26*x^69 + 20*x^68 + 69*x^67 + 40*x^66 + 101*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 34*x^7 + 104*x^6 + 90*x^5 + 20*x^4 + 109*x^3 + 40*x^2 + 77*x + 110, x^75 + 41*x^73 + 18*x^72 + 82*x^71 + 8*x^70 + 10*x^69 + 92*x^68 + 21*x^67 + 40*x^66 + 53*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 18*x^7 + 8*x^6 + 74*x^5 + 92*x^4 + 61*x^3 + 40*x^2 + 29*x + 66, x^75 + 41*x^73 + 66*x^72 + 50*x^71 + 8*x^70 + 42*x^69 + 124*x^68 + 53*x^67 + 40*x^66 + 21*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 114*x^7 + 8*x^6 + 106*x^5 + 124*x^4 + 93*x^3 + 40*x^2 + 125*x + 114, x^75 + 41*x^73 + 58*x^72 + 2*x^71 + 104*x^70 + 26*x^69 + 108*x^68 + 101*x^67 + 72*x^66 + 37*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 66*x^7 + 104*x^6 + 90*x^5 + 108*x^4 + 13*x^3 + 72*x^2 + 13*x + 10, x^75 + 41*x^73 + 122*x^72 + 2*x^71 + 104*x^70 + 26*x^69 + 108*x^68 + 101*x^67 + 72*x^66 + 37*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 66*x^7 + 104*x^6 + 90*x^5 + 108*x^4 + 13*x^3 + 72*x^2 + 13*x + 74, x^75 + 41*x^73 + 70*x^72 + 18*x^71 + 8*x^70 + 106*x^69 + 4*x^68 + 21*x^67 + 8*x^66 + 21*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 82*x^7 + 8*x^6 + 42*x^5 + 4*x^4 + 61*x^3 + 8*x^2 + 125*x + 70, x^75 + 41*x^73 + 62*x^72 + 82*x^71 + 88*x^70 + 10*x^69 + 36*x^68 + 21*x^67 + 120*x^66 + 53*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 18*x^7 + 88*x^6 + 74*x^5 + 36*x^4 + 61*x^3 + 120*x^2 + 29*x + 110, x^75 + 41*x^73 + 86*x^72 + 98*x^71 + 88*x^70 + 122*x^69 + 116*x^68 + 5*x^67 + 120*x^66 + 69*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 34*x^7 + 88*x^6 + 58*x^5 + 116*x^4 + 45*x^3 + 120*x^2 + 45*x + 6, x^75 + 41*x^73 + 114*x^72 + 2*x^71 + 56*x^70 + 58*x^69 + 12*x^68 + 37*x^67 + 56*x^66 + 69*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 66*x^7 + 56*x^6 + 122*x^5 + 12*x^4 + 77*x^3 + 56*x^2 + 45*x + 114, x^75 + 41*x^73 + 78*x^72 + 50*x^71 + 56*x^70 + 106*x^69 + 36*x^68 + 53*x^67 + 24*x^66 + 85*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 114*x^7 + 56*x^6 + 42*x^5 + 36*x^4 + 93*x^3 + 24*x^2 + 61*x + 94, x^75 + 41*x^73 + 34*x^72 + 98*x^71 + 88*x^70 + 26*x^69 + 12*x^68 + 69*x^67 + 24*x^66 + 101*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 16*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 16*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 34*x^7 + 88*x^6 + 90*x^5 + 12*x^4 + 109*x^3 + 24*x^2 + 77*x + 66, x^75 + 41*x^73 + 50*x^72 + 18*x^71 + 8*x^70 + 10*x^69 + 92*x^68 + 85*x^67 + 40*x^66 + 53*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 82*x^7 + 8*x^6 + 74*x^5 + 92*x^4 + 125*x^3 + 40*x^2 + 29*x + 34, x^75 + 41*x^73 + 34*x^72 + 18*x^71 + 40*x^70 + 74*x^69 + 28*x^68 + 85*x^67 + 8*x^66 + 117*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 82*x^7 + 40*x^6 + 10*x^5 + 28*x^4 + 125*x^3 + 8*x^2 + 93*x + 114, x^75 + 41*x^73 + 34*x^72 + 66*x^71 + 88*x^70 + 58*x^69 + 76*x^68 + 101*x^67 + 24*x^66 + 69*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 2*x^7 + 88*x^6 + 122*x^5 + 76*x^4 + 13*x^3 + 24*x^2 + 45*x + 2, x^75 + 41*x^73 + 66*x^72 + 50*x^71 + 72*x^70 + 42*x^69 + 60*x^68 + 53*x^67 + 104*x^66 + 21*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 114*x^7 + 72*x^6 + 106*x^5 + 60*x^4 + 93*x^3 + 104*x^2 + 125*x + 50, x^75 + 41*x^73 + 122*x^72 + 18*x^71 + 24*x^70 + 42*x^69 + 92*x^68 + 21*x^67 + 88*x^66 + 85*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 82*x^7 + 24*x^6 + 106*x^5 + 92*x^4 + 61*x^3 + 88*x^2 + 61*x + 26, x^75 + 41*x^73 + 54*x^72 + 66*x^71 + 56*x^70 + 90*x^69 + 20*x^68 + 37*x^67 + 24*x^66 + 101*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 2*x^7 + 56*x^6 + 26*x^5 + 20*x^4 + 77*x^3 + 24*x^2 + 77*x + 6, x^75 + 41*x^73 + 98*x^72 + 50*x^71 + 40*x^70 + 106*x^69 + 28*x^68 + 53*x^67 + 8*x^66 + 85*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 114*x^7 + 40*x^6 + 42*x^5 + 28*x^4 + 93*x^3 + 8*x^2 + 61*x + 50, x^75 + 41*x^73 + 50*x^72 + 114*x^71 + 40*x^70 + 106*x^69 + 124*x^68 + 117*x^67 + 8*x^66 + 85*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 50*x^7 + 40*x^6 + 42*x^5 + 124*x^4 + 29*x^3 + 8*x^2 + 61*x + 2, x^75 + 41*x^73 + 110*x^72 + 34*x^71 + 8*x^70 + 26*x^69 + 52*x^68 + 5*x^67 + 8*x^66 + 101*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 98*x^7 + 8*x^6 + 90*x^5 + 52*x^4 + 45*x^3 + 8*x^2 + 77*x + 110, x^75 + 41*x^73 + 114*x^72 + 114*x^71 + 72*x^70 + 106*x^69 + 28*x^68 + 117*x^67 + 104*x^66 + 85*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 50*x^7 + 72*x^6 + 42*x^5 + 28*x^4 + 29*x^3 + 104*x^2 + 61*x + 34, x^75 + 41*x^73 + 54*x^72 + 18*x^71 + 104*x^70 + 42*x^69 + 4*x^68 + 21*x^67 + 40*x^66 + 85*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 82*x^7 + 104*x^6 + 106*x^5 + 4*x^4 + 61*x^3 + 40*x^2 + 61*x + 86, x^75 + 41*x^73 + 114*x^72 + 18*x^71 + 72*x^70 + 74*x^69 + 92*x^68 + 85*x^67 + 104*x^66 + 117*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 82*x^7 + 72*x^6 + 10*x^5 + 92*x^4 + 125*x^3 + 104*x^2 + 93*x + 98, x^75 + 41*x^73 + 122*x^72 + 82*x^71 + 88*x^70 + 42*x^69 + 92*x^68 + 85*x^67 + 24*x^66 + 85*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 18*x^7 + 88*x^6 + 106*x^5 + 92*x^4 + 125*x^3 + 24*x^2 + 61*x + 26, x^75 + 41*x^73 + 102*x^72 + 66*x^71 + 120*x^70 + 90*x^69 + 52*x^68 + 37*x^67 + 88*x^66 + 101*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 2*x^7 + 120*x^6 + 26*x^5 + 52*x^4 + 77*x^3 + 88*x^2 + 77*x + 54, x^75 + 41*x^73 + 122*x^72 + 50*x^71 + 56*x^70 + 10*x^69 + 60*x^68 + 117*x^67 + 56*x^66 + 117*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 114*x^7 + 56*x^6 + 74*x^5 + 60*x^4 + 29*x^3 + 56*x^2 + 93*x + 58, x^75 + 41*x^73 + 70*x^72 + 18*x^71 + 72*x^70 + 106*x^69 + 68*x^68 + 21*x^67 + 72*x^66 + 21*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 82*x^7 + 72*x^6 + 42*x^5 + 68*x^4 + 61*x^3 + 72*x^2 + 125*x + 6, x^75 + 41*x^73 + 62*x^72 + 66*x^71 + 104*x^70 + 122*x^69 + 116*x^68 + 101*x^67 + 40*x^66 + 5*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 2*x^7 + 104*x^6 + 58*x^5 + 116*x^4 + 13*x^3 + 40*x^2 + 109*x + 94, x^75 + 41*x^73 + 98*x^72 + 18*x^71 + 40*x^70 + 74*x^69 + 28*x^68 + 85*x^67 + 8*x^66 + 117*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 82*x^7 + 40*x^6 + 10*x^5 + 28*x^4 + 125*x^3 + 8*x^2 + 93*x + 50, x^75 + 41*x^73 + 110*x^72 + 82*x^71 + 88*x^70 + 74*x^69 + 68*x^68 + 21*x^67 + 120*x^66 + 117*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 18*x^7 + 88*x^6 + 10*x^5 + 68*x^4 + 61*x^3 + 120*x^2 + 93*x + 30, x^75 + 41*x^73 + 126*x^72 + 2*x^71 + 104*x^70 + 122*x^69 + 52*x^68 + 37*x^67 + 40*x^66 + 5*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 66*x^7 + 104*x^6 + 58*x^5 + 52*x^4 + 77*x^3 + 40*x^2 + 109*x + 94, x^75 + 41*x^73 + 50*x^72 + 18*x^71 + 8*x^70 + 74*x^69 + 28*x^68 + 85*x^67 + 40*x^66 + 117*x^65 + 18*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 82*x^7 + 8*x^6 + 10*x^5 + 28*x^4 + 125*x^3 + 40*x^2 + 93*x + 98, x^75 + 41*x^73 + 122*x^72 + 114*x^71 + 120*x^70 + 74*x^69 + 124*x^68 + 53*x^67 + 120*x^66 + 53*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 50*x^7 + 120*x^6 + 10*x^5 + 124*x^4 + 93*x^3 + 120*x^2 + 29*x + 122, x^75 + 41*x^73 + 66*x^72 + 34*x^71 + 56*x^70 + 90*x^69 + 44*x^68 + 5*x^67 + 56*x^66 + 37*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 98*x^7 + 56*x^6 + 26*x^5 + 44*x^4 + 45*x^3 + 56*x^2 + 13*x + 2, x^75 + 41*x^73 + 22*x^72 + 98*x^71 + 56*x^70 + 58*x^69 + 20*x^68 + 5*x^67 + 24*x^66 + 5*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 34*x^7 + 56*x^6 + 122*x^5 + 20*x^4 + 45*x^3 + 24*x^2 + 109*x + 38, x^75 + 41*x^73 + 30*x^72 + 18*x^71 + 120*x^70 + 10*x^69 + 68*x^68 + 85*x^67 + 88*x^66 + 53*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 82*x^7 + 120*x^6 + 74*x^5 + 68*x^4 + 125*x^3 + 88*x^2 + 29*x + 110, x^75 + 41*x^73 + 102*x^72 + 2*x^71 + 88*x^70 + 26*x^69 + 20*x^68 + 101*x^67 + 120*x^66 + 37*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 66*x^7 + 88*x^6 + 90*x^5 + 20*x^4 + 13*x^3 + 120*x^2 + 13*x + 86, x^75 + 41*x^73 + 102*x^72 + 82*x^71 + 8*x^70 + 106*x^69 + 4*x^68 + 85*x^67 + 8*x^66 + 21*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 18*x^7 + 8*x^6 + 42*x^5 + 4*x^4 + 125*x^3 + 8*x^2 + 125*x + 38, x^75 + 41*x^73 + 58*x^72 + 66*x^71 + 8*x^70 + 26*x^69 + 76*x^68 + 37*x^67 + 40*x^66 + 37*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 2*x^7 + 8*x^6 + 90*x^5 + 76*x^4 + 77*x^3 + 40*x^2 + 13*x + 42, x^75 + 41*x^73 + 38*x^72 + 18*x^71 + 72*x^70 + 106*x^69 + 4*x^68 + 21*x^67 + 72*x^66 + 21*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 82*x^7 + 72*x^6 + 42*x^5 + 4*x^4 + 61*x^3 + 72*x^2 + 125*x + 102, x^75 + 41*x^73 + 90*x^72 + 34*x^71 + 40*x^70 + 122*x^69 + 44*x^68 + 69*x^67 + 8*x^66 + 69*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 74*x^8 + 98*x^7 + 40*x^6 + 58*x^5 + 44*x^4 + 109*x^3 + 8*x^2 + 45*x + 42, x^75 + 41*x^73 + 46*x^72 + 114*x^71 + 24*x^70 + 42*x^69 + 68*x^68 + 117*x^67 + 56*x^66 + 21*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 50*x^7 + 24*x^6 + 106*x^5 + 68*x^4 + 29*x^3 + 56*x^2 + 125*x + 94, x^75 + 41*x^73 + 34*x^72 + 50*x^71 + 104*x^70 + 42*x^69 + 28*x^68 + 53*x^67 + 72*x^66 + 21*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 114*x^7 + 104*x^6 + 106*x^5 + 28*x^4 + 93*x^3 + 72*x^2 + 125*x + 114, x^75 + 41*x^73 + 2*x^72 + 66*x^71 + 88*x^70 + 122*x^69 + 76*x^68 + 101*x^67 + 24*x^66 + 5*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 2*x^7 + 88*x^6 + 58*x^5 + 76*x^4 + 13*x^3 + 24*x^2 + 109*x + 34, x^75 + 41*x^73 + 110*x^72 + 82*x^71 + 24*x^70 + 74*x^69 + 4*x^68 + 21*x^67 + 56*x^66 + 117*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 18*x^7 + 24*x^6 + 10*x^5 + 4*x^4 + 61*x^3 + 56*x^2 + 93*x + 94, x^75 + 41*x^73 + 58*x^72 + 82*x^71 + 88*x^70 + 106*x^69 + 28*x^68 + 85*x^67 + 24*x^66 + 21*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 18*x^7 + 88*x^6 + 42*x^5 + 28*x^4 + 125*x^3 + 24*x^2 + 125*x + 26, x^75 + 41*x^73 + 82*x^72 + 50*x^71 + 72*x^70 + 42*x^69 + 92*x^68 + 53*x^67 + 104*x^66 + 21*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 114*x^7 + 72*x^6 + 106*x^5 + 92*x^4 + 93*x^3 + 104*x^2 + 125*x + 2, x^75 + 41*x^73 + 126*x^72 + 18*x^71 + 24*x^70 + 74*x^69 + 100*x^68 + 85*x^67 + 56*x^66 + 117*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 82*x^7 + 24*x^6 + 10*x^5 + 100*x^4 + 125*x^3 + 56*x^2 + 93*x + 110, x^75 + 41*x^73 + 70*x^72 + 34*x^71 + 24*x^70 + 122*x^69 + 84*x^68 + 69*x^67 + 56*x^66 + 69*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 98*x^7 + 24*x^6 + 58*x^5 + 84*x^4 + 109*x^3 + 56*x^2 + 45*x + 54, x^75 + 41*x^73 + 46*x^72 + 18*x^71 + 24*x^70 + 74*x^69 + 68*x^68 + 85*x^67 + 56*x^66 + 117*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 82*x^7 + 24*x^6 + 10*x^5 + 68*x^4 + 125*x^3 + 56*x^2 + 93*x + 94, x^75 + 41*x^73 + 10*x^72 + 34*x^71 + 8*x^70 + 58*x^69 + 44*x^68 + 69*x^67 + 40*x^66 + 5*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 98*x^7 + 8*x^6 + 122*x^5 + 44*x^4 + 109*x^3 + 40*x^2 + 109*x + 122, x^75 + 41*x^73 + 70*x^72 + 66*x^71 + 88*x^70 + 26*x^69 + 20*x^68 + 37*x^67 + 120*x^66 + 37*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 2*x^7 + 88*x^6 + 90*x^5 + 20*x^4 + 77*x^3 + 120*x^2 + 13*x + 118, x^75 + 41*x^73 + 70*x^72 + 18*x^71 + 40*x^70 + 42*x^69 + 100*x^68 + 21*x^67 + 104*x^66 + 85*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 82*x^7 + 40*x^6 + 106*x^5 + 100*x^4 + 61*x^3 + 104*x^2 + 61*x + 102, x^75 + 41*x^73 + 74*x^72 + 2*x^71 + 104*x^70 + 90*x^69 + 76*x^68 + 101*x^67 + 72*x^66 + 101*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 66*x^7 + 104*x^6 + 26*x^5 + 76*x^4 + 13*x^3 + 72*x^2 + 77*x + 26, x^75 + 41*x^73 + 30*x^72 + 18*x^71 + 88*x^70 + 10*x^69 + 36*x^68 + 85*x^67 + 120*x^66 + 53*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 82*x^7 + 88*x^6 + 74*x^5 + 36*x^4 + 125*x^3 + 120*x^2 + 29*x + 14, x^75 + 41*x^73 + 114*x^72 + 18*x^71 + 104*x^70 + 74*x^69 + 124*x^68 + 85*x^67 + 72*x^66 + 117*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 82*x^7 + 104*x^6 + 10*x^5 + 124*x^4 + 125*x^3 + 72*x^2 + 93*x + 66, x^75 + 41*x^73 + 78*x^72 + 50*x^71 + 120*x^70 + 42*x^69 + 36*x^68 + 53*x^67 + 88*x^66 + 21*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 80*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 16*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 114*x^7 + 120*x^6 + 106*x^5 + 36*x^4 + 93*x^3 + 88*x^2 + 125*x + 94, x^75 + 41*x^73 + 74*x^72 + 82*x^71 + 120*x^70 + 106*x^69 + 92*x^68 + 85*x^67 + 120*x^66 + 21*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 18*x^7 + 120*x^6 + 42*x^5 + 92*x^4 + 125*x^3 + 120*x^2 + 125*x + 74, x^75 + 41*x^73 + 82*x^72 + 114*x^71 + 8*x^70 + 42*x^69 + 92*x^68 + 117*x^67 + 40*x^66 + 21*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 50*x^7 + 8*x^6 + 106*x^5 + 92*x^4 + 29*x^3 + 40*x^2 + 125*x + 2, x^75 + 41*x^73 + 6*x^72 + 98*x^71 + 24*x^70 + 122*x^69 + 20*x^68 + 5*x^67 + 56*x^66 + 69*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 34*x^7 + 24*x^6 + 58*x^5 + 20*x^4 + 45*x^3 + 56*x^2 + 45*x + 54, x^75 + 41*x^73 + 74*x^72 + 114*x^71 + 88*x^70 + 10*x^69 + 60*x^68 + 53*x^67 + 24*x^66 + 117*x^65 + 90*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 50*x^7 + 88*x^6 + 74*x^5 + 60*x^4 + 93*x^3 + 24*x^2 + 93*x + 106, x^75 + 41*x^73 + 30*x^72 + 34*x^71 + 8*x^70 + 26*x^69 + 20*x^68 + 5*x^67 + 8*x^66 + 101*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 98*x^7 + 8*x^6 + 90*x^5 + 20*x^4 + 45*x^3 + 8*x^2 + 77*x + 94, x^75 + 41*x^73 + 110*x^72 + 2*x^71 + 104*x^70 + 58*x^69 + 84*x^68 + 37*x^67 + 40*x^66 + 69*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 76*x^39 + 112*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 112*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 66*x^7 + 104*x^6 + 122*x^5 + 84*x^4 + 77*x^3 + 40*x^2 + 45*x + 78, x^75 + 41*x^73 + 114*x^72 + 34*x^71 + 120*x^70 + 90*x^69 + 76*x^68 + 5*x^67 + 120*x^66 + 37*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 72*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 98*x^7 + 120*x^6 + 26*x^5 + 76*x^4 + 45*x^3 + 120*x^2 + 13*x + 50, x^75 + 41*x^73 + 70*x^72 + 18*x^71 + 104*x^70 + 42*x^69 + 36*x^68 + 21*x^67 + 40*x^66 + 85*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 82*x^7 + 104*x^6 + 106*x^5 + 36*x^4 + 61*x^3 + 40*x^2 + 61*x + 38, x^75 + 41*x^73 + 14*x^72 + 98*x^71 + 72*x^70 + 90*x^69 + 52*x^68 + 69*x^67 + 72*x^66 + 37*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 34*x^7 + 72*x^6 + 26*x^5 + 52*x^4 + 109*x^3 + 72*x^2 + 13*x + 78, x^75 + 41*x^73 + 114*x^72 + 82*x^71 + 40*x^70 + 10*x^69 + 60*x^68 + 21*x^67 + 8*x^66 + 53*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 112*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 48*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 18*x^7 + 40*x^6 + 74*x^5 + 60*x^4 + 61*x^3 + 8*x^2 + 29*x + 2, x^75 + 41*x^73 + 126*x^72 + 82*x^71 + 88*x^70 + 10*x^69 + 36*x^68 + 21*x^67 + 120*x^66 + 53*x^65 + 126*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 18*x^7 + 88*x^6 + 74*x^5 + 36*x^4 + 61*x^3 + 120*x^2 + 29*x + 46, x^75 + 41*x^73 + 58*x^72 + 34*x^71 + 40*x^70 + 122*x^69 + 108*x^68 + 69*x^67 + 8*x^66 + 69*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 98*x^7 + 40*x^6 + 58*x^5 + 108*x^4 + 109*x^3 + 8*x^2 + 45*x + 10, x^75 + 41*x^73 + 110*x^72 + 114*x^71 + 88*x^70 + 42*x^69 + 4*x^68 + 117*x^67 + 120*x^66 + 21*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 50*x^7 + 88*x^6 + 106*x^5 + 4*x^4 + 29*x^3 + 120*x^2 + 125*x + 94, x^75 + 41*x^73 + 118*x^72 + 66*x^71 + 88*x^70 + 90*x^69 + 52*x^68 + 37*x^67 + 120*x^66 + 101*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 2*x^7 + 88*x^6 + 26*x^5 + 52*x^4 + 77*x^3 + 120*x^2 + 77*x + 38, x^75 + 41*x^73 + 98*x^72 + 2*x^71 + 88*x^70 + 122*x^69 + 76*x^68 + 37*x^67 + 24*x^66 + 5*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 66*x^7 + 88*x^6 + 58*x^5 + 76*x^4 + 77*x^3 + 24*x^2 + 109*x + 66, x^75 + 41*x^73 + 110*x^72 + 18*x^71 + 24*x^70 + 74*x^69 + 68*x^68 + 85*x^67 + 56*x^66 + 117*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 62*x^8 + 82*x^7 + 24*x^6 + 10*x^5 + 68*x^4 + 125*x^3 + 56*x^2 + 93*x + 30, x^75 + 41*x^73 + 58*x^72 + 50*x^71 + 56*x^70 + 10*x^69 + 60*x^68 + 117*x^67 + 56*x^66 + 117*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 114*x^7 + 56*x^6 + 74*x^5 + 60*x^4 + 29*x^3 + 56*x^2 + 93*x + 122, x^75 + 41*x^73 + 22*x^72 + 114*x^71 + 40*x^70 + 10*x^69 + 4*x^68 + 53*x^67 + 104*x^66 + 117*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 50*x^7 + 40*x^6 + 74*x^5 + 4*x^4 + 93*x^3 + 104*x^2 + 93*x + 118, x^75 + 41*x^73 + 62*x^72 + 2*x^71 + 72*x^70 + 58*x^69 + 84*x^68 + 37*x^67 + 72*x^66 + 69*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 120*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 66*x^7 + 72*x^6 + 122*x^5 + 84*x^4 + 77*x^3 + 72*x^2 + 45*x + 126, x^75 + 41*x^73 + 26*x^72 + 114*x^71 + 120*x^70 + 74*x^69 + 60*x^68 + 53*x^67 + 120*x^66 + 53*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 50*x^7 + 120*x^6 + 10*x^5 + 60*x^4 + 93*x^3 + 120*x^2 + 29*x + 26, x^75 + 41*x^73 + 62*x^72 + 82*x^71 + 24*x^70 + 74*x^69 + 36*x^68 + 21*x^67 + 56*x^66 + 117*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 88*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 18*x^7 + 24*x^6 + 10*x^5 + 36*x^4 + 61*x^3 + 56*x^2 + 93*x + 110, x^75 + 41*x^73 + 26*x^72 + 50*x^71 + 24*x^70 + 10*x^69 + 92*x^68 + 117*x^67 + 88*x^66 + 117*x^65 + 106*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 108*x^39 + 16*x^38 + 124*x^37 + 40*x^36 + 86*x^35 + 16*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 114*x^7 + 24*x^6 + 74*x^5 + 92*x^4 + 29*x^3 + 88*x^2 + 93*x + 122, x^75 + 41*x^73 + 106*x^72 + 2*x^71 + 8*x^70 + 26*x^69 + 108*x^68 + 101*x^67 + 40*x^66 + 37*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 48*x^38 + 92*x^37 + 8*x^36 + 118*x^35 + 112*x^34 + 54*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 66*x^7 + 8*x^6 + 90*x^5 + 108*x^4 + 13*x^3 + 40*x^2 + 13*x + 90, x^75 + 41*x^73 + 58*x^72 + 18*x^71 + 56*x^70 + 42*x^69 + 124*x^68 + 21*x^67 + 56*x^66 + 85*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 80*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 80*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 82*x^7 + 56*x^6 + 106*x^5 + 124*x^4 + 61*x^3 + 56*x^2 + 61*x + 58, x^75 + 41*x^73 + 6*x^72 + 66*x^71 + 56*x^70 + 26*x^69 + 116*x^68 + 37*x^67 + 24*x^66 + 37*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 2*x^7 + 56*x^6 + 90*x^5 + 116*x^4 + 77*x^3 + 24*x^2 + 13*x + 86, x^75 + 41*x^73 + 38*x^72 + 82*x^71 + 8*x^70 + 42*x^69 + 68*x^68 + 85*x^67 + 8*x^66 + 85*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 24*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 18*x^7 + 8*x^6 + 106*x^5 + 68*x^4 + 125*x^3 + 8*x^2 + 61*x + 38, x^75 + 41*x^73 + 86*x^72 + 66*x^71 + 56*x^70 + 26*x^69 + 20*x^68 + 37*x^67 + 24*x^66 + 37*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 2*x^7 + 56*x^6 + 90*x^5 + 20*x^4 + 77*x^3 + 24*x^2 + 13*x + 102, x^75 + 41*x^73 + 106*x^72 + 2*x^71 + 40*x^70 + 26*x^69 + 12*x^68 + 101*x^67 + 8*x^66 + 37*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 12*x^40 + 76*x^39 + 112*x^38 + 92*x^37 + 72*x^36 + 118*x^35 + 48*x^34 + 54*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 90*x^8 + 66*x^7 + 40*x^6 + 90*x^5 + 12*x^4 + 13*x^3 + 8*x^2 + 13*x + 58, x^75 + 41*x^73 + 74*x^72 + 34*x^71 + 104*x^70 + 58*x^69 + 12*x^68 + 69*x^67 + 72*x^66 + 5*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 58*x^8 + 98*x^7 + 104*x^6 + 122*x^5 + 12*x^4 + 109*x^3 + 72*x^2 + 109*x + 90, x^75 + 41*x^73 + 38*x^72 + 66*x^71 + 56*x^70 + 90*x^69 + 116*x^68 + 37*x^67 + 24*x^66 + 101*x^65 + 70*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 2*x^7 + 56*x^6 + 26*x^5 + 116*x^4 + 77*x^3 + 24*x^2 + 77*x + 54, x^75 + 41*x^73 + 62*x^72 + 34*x^71 + 104*x^70 + 90*x^69 + 116*x^68 + 5*x^67 + 40*x^66 + 37*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 98*x^7 + 104*x^6 + 26*x^5 + 116*x^4 + 45*x^3 + 40*x^2 + 13*x + 94, x^75 + 41*x^73 + 98*x^72 + 34*x^71 + 120*x^70 + 26*x^69 + 108*x^68 + 5*x^67 + 120*x^66 + 101*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 12*x^39 + 80*x^38 + 92*x^37 + 8*x^36 + 54*x^35 + 80*x^34 + 54*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 98*x^7 + 120*x^6 + 90*x^5 + 108*x^4 + 45*x^3 + 120*x^2 + 77*x + 34, x^75 + 41*x^73 + 50*x^72 + 82*x^71 + 72*x^70 + 10*x^69 + 92*x^68 + 21*x^67 + 104*x^66 + 53*x^65 + 82*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 28*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 98*x^8 + 18*x^7 + 72*x^6 + 74*x^5 + 92*x^4 + 61*x^3 + 104*x^2 + 29*x + 34, x^75 + 41*x^73 + 86*x^72 + 82*x^71 + 8*x^70 + 42*x^69 + 36*x^68 + 85*x^67 + 8*x^66 + 85*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 18*x^7 + 8*x^6 + 106*x^5 + 36*x^4 + 125*x^3 + 8*x^2 + 61*x + 22, x^75 + 41*x^73 + 78*x^72 + 18*x^71 + 88*x^70 + 74*x^69 + 68*x^68 + 85*x^67 + 120*x^66 + 117*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 82*x^7 + 88*x^6 + 10*x^5 + 68*x^4 + 125*x^3 + 120*x^2 + 93*x + 62, x^75 + 41*x^73 + 14*x^72 + 98*x^71 + 8*x^70 + 90*x^69 + 116*x^68 + 69*x^67 + 8*x^66 + 37*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 34*x^7 + 8*x^6 + 26*x^5 + 116*x^4 + 109*x^3 + 8*x^2 + 13*x + 14, x^75 + 41*x^73 + 86*x^72 + 114*x^71 + 40*x^70 + 74*x^69 + 68*x^68 + 53*x^67 + 104*x^66 + 53*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 102*x^8 + 50*x^7 + 40*x^6 + 10*x^5 + 68*x^4 + 93*x^3 + 104*x^2 + 29*x + 118, x^75 + 41*x^73 + 2*x^72 + 50*x^71 + 72*x^70 + 106*x^69 + 124*x^68 + 53*x^67 + 104*x^66 + 85*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 104*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 114*x^7 + 72*x^6 + 42*x^5 + 124*x^4 + 93*x^3 + 104*x^2 + 61*x + 50, x^75 + 41*x^73 + 18*x^72 + 18*x^71 + 72*x^70 + 74*x^69 + 28*x^68 + 85*x^67 + 104*x^66 + 117*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 40*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 66*x^8 + 82*x^7 + 72*x^6 + 10*x^5 + 28*x^4 + 125*x^3 + 104*x^2 + 93*x + 2, x^75 + 41*x^73 + 14*x^72 + 98*x^71 + 8*x^70 + 26*x^69 + 52*x^68 + 69*x^67 + 8*x^66 + 101*x^65 + 30*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 34*x^7 + 8*x^6 + 90*x^5 + 52*x^4 + 109*x^3 + 8*x^2 + 77*x + 78, x^75 + 41*x^73 + 10*x^72 + 34*x^71 + 104*x^70 + 122*x^69 + 76*x^68 + 69*x^67 + 72*x^66 + 69*x^65 + 74*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 98*x^7 + 104*x^6 + 58*x^5 + 76*x^4 + 109*x^3 + 72*x^2 + 45*x + 90, x^75 + 41*x^73 + 126*x^72 + 34*x^71 + 104*x^70 + 26*x^69 + 52*x^68 + 5*x^67 + 40*x^66 + 101*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 98*x^7 + 104*x^6 + 90*x^5 + 52*x^4 + 45*x^3 + 40*x^2 + 77*x + 94, x^75 + 41*x^73 + 14*x^72 + 2*x^71 + 72*x^70 + 58*x^69 + 116*x^68 + 37*x^67 + 72*x^66 + 69*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 76*x^39 + 48*x^38 + 28*x^37 + 56*x^36 + 118*x^35 + 48*x^34 + 118*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 66*x^7 + 72*x^6 + 122*x^5 + 116*x^4 + 77*x^3 + 72*x^2 + 45*x + 14, x^75 + 41*x^73 + 22*x^72 + 34*x^71 + 120*x^70 + 58*x^69 + 20*x^68 + 69*x^67 + 88*x^66 + 5*x^65 + 54*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 98*x^7 + 120*x^6 + 122*x^5 + 20*x^4 + 109*x^3 + 88*x^2 + 109*x + 38, x^75 + 41*x^73 + 114*x^72 + 66*x^71 + 120*x^70 + 122*x^69 + 76*x^68 + 101*x^67 + 120*x^66 + 5*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 124*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 34*x^8 + 2*x^7 + 120*x^6 + 58*x^5 + 76*x^4 + 13*x^3 + 120*x^2 + 109*x + 50, x^75 + 41*x^73 + 22*x^72 + 98*x^71 + 88*x^70 + 58*x^69 + 52*x^68 + 5*x^67 + 120*x^66 + 5*x^65 + 22*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 12*x^39 + 16*x^38 + 28*x^37 + 56*x^36 + 54*x^35 + 80*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 34*x^7 + 88*x^6 + 122*x^5 + 52*x^4 + 45*x^3 + 120*x^2 + 109*x + 6, x^75 + 41*x^73 + 54*x^72 + 114*x^71 + 8*x^70 + 74*x^69 + 100*x^68 + 53*x^67 + 8*x^66 + 53*x^65 + 6*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 48*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 48*x^34 + 22*x^33 + 52*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 50*x^7 + 8*x^6 + 10*x^5 + 100*x^4 + 93*x^3 + 8*x^2 + 29*x + 118, x^75 + 41*x^73 + 26*x^72 + 34*x^71 + 72*x^70 + 122*x^69 + 76*x^68 + 69*x^67 + 104*x^66 + 69*x^65 + 58*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 12*x^39 + 48*x^38 + 28*x^37 + 72*x^36 + 54*x^35 + 112*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 98*x^7 + 72*x^6 + 58*x^5 + 76*x^4 + 109*x^3 + 104*x^2 + 45*x + 74, x^75 + 41*x^73 + 58*x^72 + 114*x^71 + 120*x^70 + 74*x^69 + 124*x^68 + 53*x^67 + 120*x^66 + 53*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 108*x^39 + 80*x^38 + 124*x^37 + 104*x^36 + 86*x^35 + 80*x^34 + 22*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 42*x^8 + 50*x^7 + 120*x^6 + 10*x^5 + 124*x^4 + 93*x^3 + 120*x^2 + 29*x + 58, x^75 + 41*x^73 + 38*x^72 + 82*x^71 + 40*x^70 + 106*x^69 + 36*x^68 + 85*x^67 + 104*x^66 + 21*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 18*x^7 + 40*x^6 + 42*x^5 + 36*x^4 + 125*x^3 + 104*x^2 + 125*x + 70, x^75 + 41*x^73 + 46*x^72 + 18*x^71 + 88*x^70 + 10*x^69 + 68*x^68 + 85*x^67 + 120*x^66 + 53*x^65 + 46*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 82*x^7 + 88*x^6 + 74*x^5 + 68*x^4 + 125*x^3 + 120*x^2 + 29*x + 94, x^75 + 41*x^73 + 66*x^72 + 82*x^71 + 72*x^70 + 10*x^69 + 124*x^68 + 21*x^67 + 104*x^66 + 53*x^65 + 34*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 18*x^7 + 72*x^6 + 74*x^5 + 124*x^4 + 61*x^3 + 104*x^2 + 29*x + 114, x^75 + 41*x^73 + 98*x^72 + 18*x^71 + 8*x^70 + 10*x^69 + 60*x^68 + 85*x^67 + 40*x^66 + 53*x^65 + 66*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 18*x^8 + 82*x^7 + 8*x^6 + 74*x^5 + 60*x^4 + 125*x^3 + 40*x^2 + 29*x + 18, x^75 + 41*x^73 + 122*x^72 + 34*x^71 + 40*x^70 + 58*x^69 + 44*x^68 + 69*x^67 + 8*x^66 + 5*x^65 + 122*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 12*x^39 + 112*x^38 + 28*x^37 + 8*x^36 + 54*x^35 + 48*x^34 + 118*x^33 + 76*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 98*x^7 + 40*x^6 + 122*x^5 + 44*x^4 + 109*x^3 + 8*x^2 + 109*x + 10, x^75 + 41*x^73 + 38*x^72 + 114*x^71 + 104*x^70 + 74*x^69 + 36*x^68 + 53*x^67 + 40*x^66 + 53*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 54*x^8 + 50*x^7 + 104*x^6 + 10*x^5 + 36*x^4 + 93*x^3 + 40*x^2 + 29*x + 70, x^75 + 41*x^73 + 34*x^72 + 2*x^71 + 88*x^70 + 58*x^69 + 12*x^68 + 37*x^67 + 24*x^66 + 69*x^65 + 114*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 28*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 72*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 82*x^8 + 66*x^7 + 88*x^6 + 122*x^5 + 12*x^4 + 77*x^3 + 24*x^2 + 45*x + 66, x^75 + 41*x^73 + 102*x^72 + 66*x^71 + 24*x^70 + 90*x^69 + 84*x^68 + 37*x^67 + 56*x^66 + 101*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 76*x^39 + 16*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 80*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 2*x^7 + 24*x^6 + 26*x^5 + 84*x^4 + 77*x^3 + 56*x^2 + 77*x + 22, x^75 + 41*x^73 + 70*x^72 + 66*x^71 + 120*x^70 + 26*x^69 + 52*x^68 + 37*x^67 + 88*x^66 + 37*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 56*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 86*x^8 + 2*x^7 + 120*x^6 + 90*x^5 + 52*x^4 + 77*x^3 + 88*x^2 + 13*x + 86, x^75 + 41*x^73 + 2*x^72 + 2*x^71 + 56*x^70 + 122*x^69 + 108*x^68 + 37*x^67 + 56*x^66 + 5*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 76*x^39 + 80*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 80*x^34 + 118*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 66*x^7 + 56*x^6 + 58*x^5 + 108*x^4 + 77*x^3 + 56*x^2 + 109*x + 2, x^75 + 41*x^73 + 22*x^72 + 82*x^71 + 8*x^70 + 106*x^69 + 100*x^68 + 85*x^67 + 8*x^66 + 21*x^65 + 38*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 44*x^39 + 48*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 48*x^34 + 86*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 18*x^7 + 8*x^6 + 42*x^5 + 100*x^4 + 125*x^3 + 8*x^2 + 125*x + 22, x^75 + 41*x^73 + 78*x^72 + 50*x^71 + 88*x^70 + 106*x^69 + 68*x^68 + 53*x^67 + 120*x^66 + 85*x^65 + 14*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 24*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 30*x^8 + 114*x^7 + 88*x^6 + 42*x^5 + 68*x^4 + 93*x^3 + 120*x^2 + 61*x + 62, x^75 + 41*x^73 + 26*x^72 + 18*x^71 + 24*x^70 + 42*x^69 + 28*x^68 + 21*x^67 + 88*x^66 + 85*x^65 + 42*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 44*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 108*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 10*x^8 + 82*x^7 + 24*x^6 + 106*x^5 + 28*x^4 + 61*x^3 + 88*x^2 + 61*x + 58, x^75 + 41*x^73 + 62*x^72 + 18*x^71 + 56*x^70 + 74*x^69 + 4*x^68 + 85*x^67 + 24*x^66 + 117*x^65 + 94*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 44*x^39 + 80*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 16*x^34 + 22*x^33 + 4*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 14*x^8 + 82*x^7 + 56*x^6 + 10*x^5 + 4*x^4 + 125*x^3 + 24*x^2 + 93*x + 14, x^75 + 41*x^73 + 82*x^72 + 50*x^71 + 8*x^70 + 106*x^69 + 92*x^68 + 53*x^67 + 40*x^66 + 85*x^65 + 50*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 8*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 108*x^39 + 48*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 112*x^34 + 86*x^33 + 92*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 104*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 114*x^7 + 8*x^6 + 42*x^5 + 92*x^4 + 93*x^3 + 40*x^2 + 61*x + 2, x^75 + 41*x^73 + 66*x^72 + 18*x^71 + 8*x^70 + 74*x^69 + 60*x^68 + 85*x^67 + 40*x^66 + 117*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 44*x^39 + 48*x^38 + 124*x^37 + 104*x^36 + 22*x^35 + 112*x^34 + 22*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 114*x^8 + 82*x^7 + 8*x^6 + 10*x^5 + 60*x^4 + 125*x^3 + 40*x^2 + 93*x + 50, x^75 + 41*x^73 + 126*x^72 + 114*x^71 + 88*x^70 + 106*x^69 + 100*x^68 + 117*x^67 + 120*x^66 + 85*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 108*x^39 + 16*x^38 + 60*x^37 + 88*x^36 + 86*x^35 + 80*x^34 + 86*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 50*x^7 + 88*x^6 + 42*x^5 + 100*x^4 + 29*x^3 + 120*x^2 + 61*x + 110, x^75 + 41*x^73 + 14*x^72 + 18*x^71 + 88*x^70 + 74*x^69 + 68*x^68 + 85*x^67 + 120*x^66 + 117*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 4*x^40 + 44*x^39 + 16*x^38 + 124*x^37 + 24*x^36 + 22*x^35 + 80*x^34 + 22*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 94*x^8 + 82*x^7 + 88*x^6 + 10*x^5 + 68*x^4 + 125*x^3 + 120*x^2 + 93*x + 126, x^75 + 41*x^73 + 10*x^72 + 82*x^71 + 24*x^70 + 42*x^69 + 60*x^68 + 85*x^67 + 88*x^66 + 85*x^65 + 26*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 8*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 40*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 76*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 104*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 12*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 40*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 8*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 122*x^8 + 18*x^7 + 24*x^6 + 106*x^5 + 60*x^4 + 125*x^3 + 88*x^2 + 61*x + 42, x^75 + 41*x^73 + 122*x^72 + 18*x^71 + 88*x^70 + 106*x^69 + 92*x^68 + 21*x^67 + 24*x^66 + 21*x^65 + 10*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 72*x^56 + 56*x^55 + 32*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 32*x^50 + 20*x^49 + 104*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 108*x^40 + 44*x^39 + 16*x^38 + 60*x^37 + 40*x^36 + 22*x^35 + 16*x^34 + 86*x^33 + 44*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 104*x^24 + 56*x^23 + 32*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 32*x^18 + 4*x^17 + 72*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 106*x^8 + 82*x^7 + 88*x^6 + 42*x^5 + 92*x^4 + 61*x^3 + 24*x^2 + 125*x + 26, x^75 + 41*x^73 + 30*x^72 + 98*x^71 + 104*x^70 + 90*x^69 + 116*x^68 + 69*x^67 + 40*x^66 + 37*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 100*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 110*x^8 + 34*x^7 + 104*x^6 + 26*x^5 + 116*x^4 + 109*x^3 + 40*x^2 + 13*x + 126, x^75 + 41*x^73 + 46*x^72 + 98*x^71 + 72*x^70 + 90*x^69 + 116*x^68 + 69*x^67 + 72*x^66 + 37*x^65 + 62*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 88*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 56*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 68*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 68*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 56*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 88*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 126*x^8 + 34*x^7 + 72*x^6 + 26*x^5 + 116*x^4 + 109*x^3 + 72*x^2 + 13*x + 110, x^75 + 41*x^73 + 22*x^72 + 2*x^71 + 56*x^70 + 26*x^69 + 84*x^68 + 101*x^67 + 24*x^66 + 37*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 116*x^40 + 76*x^39 + 80*x^38 + 92*x^37 + 120*x^36 + 118*x^35 + 16*x^34 + 54*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 38*x^8 + 66*x^7 + 56*x^6 + 90*x^5 + 84*x^4 + 13*x^3 + 24*x^2 + 13*x + 102, x^75 + 41*x^73 + 6*x^72 + 18*x^71 + 40*x^70 + 106*x^69 + 36*x^68 + 21*x^67 + 104*x^66 + 21*x^65 + 118*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 20*x^40 + 44*x^39 + 112*x^38 + 60*x^37 + 88*x^36 + 22*x^35 + 112*x^34 + 86*x^33 + 84*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 22*x^8 + 82*x^7 + 40*x^6 + 42*x^5 + 36*x^4 + 61*x^3 + 104*x^2 + 125*x + 102, x^75 + 41*x^73 + 2*x^72 + 114*x^71 + 40*x^70 + 42*x^69 + 92*x^68 + 117*x^67 + 8*x^66 + 21*x^65 + 2*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 104*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 16*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 92*x^40 + 108*x^39 + 112*x^38 + 60*x^37 + 40*x^36 + 86*x^35 + 48*x^34 + 86*x^33 + 60*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 8*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 16*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 50*x^8 + 50*x^7 + 40*x^6 + 106*x^5 + 92*x^4 + 29*x^3 + 8*x^2 + 125*x + 82, x^75 + 41*x^73 + 82*x^72 + 2*x^71 + 88*x^70 + 58*x^69 + 108*x^68 + 37*x^67 + 24*x^66 + 69*x^65 + 98*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 32*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 40*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 80*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 72*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 96*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 60*x^40 + 76*x^39 + 16*x^38 + 28*x^37 + 8*x^36 + 118*x^35 + 16*x^34 + 118*x^33 + 124*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 96*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 72*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 80*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 40*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 32*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 2*x^8 + 66*x^7 + 88*x^6 + 122*x^5 + 108*x^4 + 77*x^3 + 24*x^2 + 45*x + 50, x^75 + 41*x^73 + 126*x^72 + 98*x^71 + 72*x^70 + 90*x^69 + 20*x^68 + 69*x^67 + 72*x^66 + 37*x^65 + 78*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 48*x^38 + 92*x^37 + 120*x^36 + 54*x^35 + 48*x^34 + 54*x^33 + 36*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 34*x^7 + 72*x^6 + 26*x^5 + 20*x^4 + 109*x^3 + 72*x^2 + 13*x + 126, x^75 + 41*x^73 + 118*x^72 + 34*x^71 + 56*x^70 + 58*x^69 + 20*x^68 + 69*x^67 + 24*x^66 + 5*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 120*x^55 + 32*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 32*x^50 + 84*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 12*x^39 + 80*x^38 + 28*x^37 + 120*x^36 + 54*x^35 + 16*x^34 + 118*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 120*x^23 + 32*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 32*x^18 + 68*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 6*x^8 + 98*x^7 + 56*x^6 + 122*x^5 + 20*x^4 + 109*x^3 + 24*x^2 + 109*x + 70, x^75 + 41*x^73 + 54*x^72 + 50*x^71 + 104*x^70 + 74*x^69 + 4*x^68 + 117*x^67 + 40*x^66 + 53*x^65 + 102*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 120*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 88*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 52*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 24*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 116*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 88*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 120*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 70*x^8 + 114*x^7 + 104*x^6 + 10*x^5 + 4*x^4 + 29*x^3 + 40*x^2 + 29*x + 86, x^75 + 41*x^73 + 126*x^72 + 34*x^71 + 40*x^70 + 26*x^69 + 116*x^68 + 5*x^67 + 104*x^66 + 101*x^65 + 110*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 24*x^56 + 120*x^55 + 96*x^54 + 24*x^53 + 48*x^52 + 20*x^51 + 96*x^50 + 84*x^49 + 120*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 36*x^40 + 12*x^39 + 112*x^38 + 92*x^37 + 56*x^36 + 54*x^35 + 112*x^34 + 54*x^33 + 100*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 120*x^24 + 120*x^23 + 96*x^22 + 24*x^21 + 48*x^20 + 4*x^19 + 96*x^18 + 68*x^17 + 24*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 78*x^8 + 98*x^7 + 40*x^6 + 90*x^5 + 116*x^4 + 45*x^3 + 104*x^2 + 77*x + 30, x^75 + 41*x^73 + 102*x^72 + 114*x^71 + 104*x^70 + 10*x^69 + 100*x^68 + 53*x^67 + 40*x^66 + 117*x^65 + 86*x^64 + 112*x^63 + 64*x^62 + 48*x^61 + 96*x^60 + 84*x^59 + 64*x^58 + 52*x^57 + 56*x^56 + 56*x^55 + 96*x^54 + 88*x^53 + 112*x^52 + 84*x^51 + 96*x^50 + 20*x^49 + 24*x^48 + 16*x^47 + 64*x^46 + 80*x^45 + 32*x^44 + 14*x^43 + 64*x^42 + 126*x^41 + 84*x^40 + 108*x^39 + 112*x^38 + 124*x^37 + 88*x^36 + 86*x^35 + 112*x^34 + 22*x^33 + 20*x^32 + 16*x^31 + 64*x^30 + 80*x^29 + 32*x^28 + 36*x^27 + 64*x^26 + 4*x^25 + 24*x^24 + 56*x^23 + 96*x^22 + 88*x^21 + 112*x^20 + 68*x^19 + 96*x^18 + 4*x^17 + 56*x^16 + 112*x^15 + 64*x^14 + 48*x^13 + 96*x^12 + 121*x^11 + 64*x^10 + 33*x^9 + 118*x^8 + 50*x^7 + 104*x^6 + 74*x^5 + 100*x^4 + 93*x^3 + 40*x^2 + 93*x + 70}

In [4]:
#precompute Seidel char polys classes n=73, e=7
#scc737=SeidelCharPolysMod(73,7)

In [5]:
scc737={x^73 + 60*x^71 + 60*x^70 + 78*x^69 + 116*x^68 + 76*x^67 + 100*x^66 + 49*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 78*x^5 + 52*x^4 + 12*x^3 + 36*x^2 + 25*x + 44, x^73 + 60*x^71 + 108*x^70 + 78*x^69 + 68*x^68 + 76*x^67 + 52*x^66 + 49*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 78*x^5 + 4*x^4 + 12*x^3 + 116*x^2 + 25*x + 92, x^73 + 60*x^71 + 96*x^70 + 118*x^69 + 64*x^68 + 124*x^67 + 96*x^66 + 89*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 118*x^5 + 64*x^4 + 60*x^3 + 96*x^2 + 65*x, x^73 + 60*x^71 + 28*x^70 + 94*x^69 + 100*x^68 + 108*x^67 + 100*x^66 + x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 94*x^5 + 36*x^4 + 44*x^3 + 36*x^2 + 105*x + 92, x^73 + 60*x^71 + 104*x^70 + 102*x^69 + 72*x^68 + 92*x^67 + 120*x^66 + 9*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 102*x^5 + 72*x^4 + 28*x^3 + 120*x^2 + 113*x + 88, x^73 + 60*x^71 + 52*x^70 + 46*x^69 + 124*x^68 + 12*x^67 + 108*x^66 + 17*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 46*x^5 + 60*x^4 + 76*x^3 + 44*x^2 + 121*x + 36, x^73 + 60*x^71 + 36*x^70 + 126*x^69 + 28*x^68 + 108*x^67 + 28*x^66 + 97*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 126*x^5 + 92*x^4 + 44*x^3 + 92*x^2 + 73*x + 100, x^73 + 60*x^71 + 44*x^70 + 94*x^69 + 84*x^68 + 44*x^67 + 20*x^66 + 65*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 94*x^5 + 20*x^4 + 108*x^3 + 84*x^2 + 41*x + 44, x^73 + 60*x^71 + 44*x^70 + 94*x^69 + 20*x^68 + 108*x^67 + 84*x^66 + x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 94*x^5 + 84*x^4 + 44*x^3 + 20*x^2 + 105*x + 44, x^73 + 60*x^71 + 16*x^70 + 86*x^69 + 16*x^68 + 60*x^67 + 48*x^66 + 57*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 86*x^5 + 16*x^4 + 124*x^3 + 48*x^2 + 33*x + 48, x^73 + 60*x^71 + 80*x^70 + 38*x^69 + 96*x^68 + 92*x^67 + 80*x^66 + 73*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 38*x^5 + 96*x^4 + 28*x^3 + 80*x^2 + 49*x, x^73 + 60*x^71 + 112*x^70 + 86*x^69 + 16*x^68 + 60*x^67 + 16*x^66 + 57*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 86*x^5 + 16*x^4 + 124*x^3 + 16*x^2 + 33*x + 112, x^73 + 60*x^71 + 16*x^70 + 54*x^69 + 112*x^68 + 60*x^67 + 48*x^66 + 89*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 54*x^5 + 112*x^4 + 124*x^3 + 48*x^2 + 65*x + 80, x^73 + 60*x^71 + 84*x^70 + 110*x^69 + 28*x^68 + 12*x^67 + 76*x^66 + 81*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 110*x^5 + 92*x^4 + 76*x^3 + 12*x^2 + 57*x + 4, x^73 + 60*x^71 + 32*x^70 + 86*x^69 + 32*x^68 + 60*x^67 + 96*x^66 + 57*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 86*x^5 + 32*x^4 + 124*x^3 + 96*x^2 + 33*x + 96, x^73 + 60*x^71 + 84*x^70 + 30*x^69 + 76*x^68 + 108*x^67 + 108*x^66 + 65*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 30*x^5 + 12*x^4 + 44*x^3 + 44*x^2 + 41*x + 52, x^73 + 60*x^71 + 102*x^69 + 80*x^68 + 28*x^67 + 32*x^66 + 73*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 102*x^5 + 80*x^4 + 92*x^3 + 32*x^2 + 49*x + 16, x^73 + 60*x^71 + 64*x^70 + 38*x^69 + 80*x^68 + 92*x^67 + 32*x^66 + 73*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 38*x^5 + 80*x^4 + 28*x^3 + 32*x^2 + 49*x + 80, x^73 + 60*x^71 + 86*x^69 + 64*x^68 + 124*x^67 + 64*x^66 + 121*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 86*x^5 + 64*x^4 + 60*x^3 + 64*x^2 + 97*x, x^73 + 60*x^71 + 100*x^70 + 94*x^69 + 92*x^68 + 108*x^67 + 28*x^66 + x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 94*x^5 + 28*x^4 + 44*x^3 + 92*x^2 + 105*x + 100, x^73 + 60*x^71 + 64*x^70 + 86*x^69 + 64*x^68 + 124*x^67 + 121*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 86*x^5 + 64*x^4 + 60*x^3 + 97*x, x^73 + 60*x^71 + 68*x^70 + 46*x^69 + 76*x^68 + 12*x^67 + 28*x^66 + 17*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 46*x^5 + 12*x^4 + 76*x^3 + 92*x^2 + 121*x + 20, x^73 + 60*x^71 + 8*x^70 + 38*x^69 + 104*x^68 + 92*x^67 + 88*x^66 + 73*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 38*x^5 + 104*x^4 + 28*x^3 + 88*x^2 + 49*x + 56, x^73 + 60*x^71 + 60*x^70 + 78*x^69 + 20*x^68 + 12*x^67 + 100*x^66 + 113*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 78*x^5 + 84*x^4 + 76*x^3 + 36*x^2 + 89*x + 12, x^73 + 60*x^71 + 40*x^70 + 70*x^69 + 8*x^68 + 92*x^67 + 120*x^66 + 41*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 70*x^5 + 8*x^4 + 28*x^3 + 120*x^2 + 17*x + 88, x^73 + 60*x^71 + 6*x^69 + 48*x^68 + 92*x^67 + 96*x^66 + 105*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 6*x^5 + 48*x^4 + 28*x^3 + 96*x^2 + 81*x + 112, x^73 + 60*x^71 + 56*x^70 + 38*x^69 + 88*x^68 + 92*x^67 + 104*x^66 + 73*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 38*x^5 + 88*x^4 + 28*x^3 + 104*x^2 + 49*x + 8, x^73 + 60*x^71 + 28*x^70 + 14*x^69 + 20*x^68 + 76*x^67 + 4*x^66 + 113*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 14*x^5 + 84*x^4 + 12*x^3 + 68*x^2 + 89*x + 12, x^73 + 60*x^71 + 76*x^70 + 46*x^69 + 4*x^68 + 12*x^67 + 20*x^66 + 17*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 46*x^5 + 68*x^4 + 76*x^3 + 84*x^2 + 121*x + 92, x^73 + 60*x^71 + 112*x^70 + 22*x^69 + 48*x^68 + 60*x^67 + 80*x^66 + 121*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 22*x^5 + 48*x^4 + 124*x^3 + 80*x^2 + 97*x + 16, x^73 + 60*x^71 + 76*x^70 + 14*x^69 + 4*x^68 + 12*x^67 + 84*x^66 + 49*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 14*x^5 + 68*x^4 + 76*x^3 + 20*x^2 + 25*x + 28, x^73 + 60*x^71 + 108*x^70 + 46*x^69 + 68*x^68 + 12*x^67 + 52*x^66 + 17*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 46*x^5 + 4*x^4 + 76*x^3 + 116*x^2 + 121*x + 92, x^73 + 60*x^71 + 8*x^70 + 70*x^69 + 72*x^68 + 28*x^67 + 24*x^66 + 105*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 70*x^5 + 72*x^4 + 92*x^3 + 24*x^2 + 81*x + 24, x^73 + 60*x^71 + 72*x^70 + 6*x^69 + 8*x^68 + 92*x^67 + 24*x^66 + 105*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 6*x^5 + 8*x^4 + 28*x^3 + 24*x^2 + 81*x + 24, x^73 + 60*x^71 + 88*x^70 + 6*x^69 + 56*x^68 + 92*x^67 + 8*x^66 + 105*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 6*x^5 + 56*x^4 + 28*x^3 + 8*x^2 + 81*x + 104, x^73 + 60*x^71 + 12*x^70 + 62*x^69 + 84*x^68 + 108*x^67 + 116*x^66 + 33*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 62*x^5 + 20*x^4 + 44*x^3 + 52*x^2 + 9*x + 108, x^73 + 60*x^71 + 80*x^70 + 70*x^69 + 32*x^68 + 28*x^67 + 80*x^66 + 105*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 70*x^5 + 32*x^4 + 92*x^3 + 80*x^2 + 81*x + 64, x^73 + 60*x^71 + 76*x^70 + 46*x^69 + 100*x^68 + 76*x^67 + 20*x^66 + 81*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 46*x^5 + 36*x^4 + 12*x^3 + 84*x^2 + 57*x + 124, x^73 + 60*x^71 + 8*x^70 + 118*x^69 + 88*x^68 + 124*x^67 + 120*x^66 + 89*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 118*x^5 + 88*x^4 + 60*x^3 + 120*x^2 + 65*x + 40, x^73 + 60*x^71 + 80*x^70 + 118*x^69 + 80*x^68 + 60*x^67 + 48*x^66 + 25*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 118*x^5 + 80*x^4 + 124*x^3 + 48*x^2 + x + 48, x^73 + 60*x^71 + 88*x^70 + 86*x^69 + 72*x^68 + 124*x^67 + 104*x^66 + 121*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 86*x^5 + 72*x^4 + 60*x^3 + 104*x^2 + 97*x + 120, x^73 + 60*x^71 + 56*x^70 + 102*x^69 + 120*x^68 + 92*x^67 + 40*x^66 + 9*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 102*x^5 + 120*x^4 + 28*x^3 + 40*x^2 + 113*x + 40, x^73 + 60*x^71 + 72*x^70 + 22*x^69 + 56*x^68 + 124*x^67 + 56*x^66 + 57*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 22*x^5 + 56*x^4 + 60*x^3 + 56*x^2 + 33*x + 72, x^73 + 60*x^71 + 6*x^69 + 112*x^68 + 92*x^67 + 96*x^66 + 105*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 6*x^5 + 112*x^4 + 28*x^3 + 96*x^2 + 81*x + 48, x^73 + 60*x^71 + 120*x^70 + 102*x^69 + 88*x^68 + 92*x^67 + 40*x^66 + 9*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 102*x^5 + 88*x^4 + 28*x^3 + 40*x^2 + 113*x + 8, x^73 + 60*x^71 + 108*x^70 + 62*x^69 + 84*x^68 + 108*x^67 + 84*x^66 + 33*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 62*x^5 + 20*x^4 + 44*x^3 + 20*x^2 + 9*x + 44, x^73 + 60*x^71 + 96*x^70 + 70*x^69 + 48*x^68 + 28*x^67 + 105*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 70*x^5 + 48*x^4 + 92*x^3 + 81*x + 112, x^73 + 60*x^71 + 12*x^70 + 110*x^69 + 68*x^68 + 76*x^67 + 20*x^66 + 17*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 110*x^5 + 4*x^4 + 12*x^3 + 84*x^2 + 121*x + 92, x^73 + 60*x^71 + 44*x^70 + 110*x^69 + 100*x^68 + 12*x^67 + 52*x^66 + 81*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 110*x^5 + 36*x^4 + 76*x^3 + 116*x^2 + 57*x + 124, x^73 + 60*x^71 + 20*x^70 + 110*x^69 + 124*x^68 + 12*x^67 + 76*x^66 + 81*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 110*x^5 + 60*x^4 + 76*x^3 + 12*x^2 + 57*x + 100, x^73 + 60*x^71 + 8*x^70 + 118*x^69 + 120*x^68 + 60*x^67 + 120*x^66 + 25*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 118*x^5 + 120*x^4 + 124*x^3 + 120*x^2 + x + 8, x^73 + 60*x^71 + 124*x^70 + 78*x^69 + 52*x^68 + 76*x^67 + 36*x^66 + 49*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 78*x^5 + 116*x^4 + 12*x^3 + 100*x^2 + 25*x + 108, x^73 + 60*x^71 + 64*x^70 + 118*x^69 + 32*x^68 + 60*x^67 + 64*x^66 + 25*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 118*x^5 + 32*x^4 + 124*x^3 + 64*x^2 + x + 96, x^73 + 60*x^71 + 76*x^70 + 14*x^69 + 36*x^68 + 76*x^67 + 84*x^66 + 113*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 14*x^5 + 100*x^4 + 12*x^3 + 20*x^2 + 89*x + 124, x^73 + 60*x^71 + 88*x^70 + 38*x^69 + 120*x^68 + 92*x^67 + 72*x^66 + 73*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 38*x^5 + 120*x^4 + 28*x^3 + 72*x^2 + 49*x + 104, x^73 + 60*x^71 + 92*x^70 + 30*x^69 + 4*x^68 + 108*x^67 + 100*x^66 + 65*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 30*x^5 + 68*x^4 + 44*x^3 + 36*x^2 + 41*x + 124, x^73 + 60*x^71 + 92*x^70 + 62*x^69 + 100*x^68 + 44*x^67 + 36*x^66 + 97*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 62*x^5 + 36*x^4 + 108*x^3 + 100*x^2 + 73*x + 92, x^73 + 60*x^71 + 60*x^70 + 94*x^69 + 68*x^68 + 108*x^67 + 68*x^66 + x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 94*x^5 + 4*x^4 + 44*x^3 + 4*x^2 + 105*x + 124, x^73 + 60*x^71 + 12*x^70 + 46*x^69 + 68*x^68 + 76*x^67 + 20*x^66 + 81*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 46*x^5 + 4*x^4 + 12*x^3 + 84*x^2 + 57*x + 92, x^73 + 60*x^71 + 84*x^70 + 126*x^69 + 108*x^68 + 44*x^67 + 44*x^66 + 33*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 126*x^5 + 44*x^4 + 108*x^3 + 108*x^2 + 9*x + 84, x^73 + 60*x^71 + 32*x^70 + 86*x^69 + 60*x^67 + 32*x^66 + 57*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 86*x^5 + 124*x^3 + 32*x^2 + 33*x + 64, x^73 + 60*x^71 + 72*x^70 + 102*x^69 + 104*x^68 + 28*x^67 + 88*x^66 + 73*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 102*x^5 + 104*x^4 + 92*x^3 + 88*x^2 + 49*x + 120, x^73 + 60*x^71 + 20*x^70 + 62*x^69 + 12*x^68 + 108*x^67 + 108*x^66 + 33*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 62*x^5 + 76*x^4 + 44*x^3 + 44*x^2 + 9*x + 52, x^73 + 60*x^71 + 28*x^70 + 46*x^69 + 52*x^68 + 76*x^67 + 4*x^66 + 81*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 46*x^5 + 116*x^4 + 12*x^3 + 68*x^2 + 57*x + 108, x^73 + 60*x^71 + 124*x^70 + 46*x^69 + 84*x^68 + 12*x^67 + 100*x^66 + 17*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 46*x^5 + 20*x^4 + 76*x^3 + 36*x^2 + 121*x + 12, x^73 + 60*x^71 + 100*x^70 + 126*x^69 + 28*x^68 + 44*x^67 + 28*x^66 + 33*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 126*x^5 + 92*x^4 + 108*x^3 + 92*x^2 + 9*x + 36, x^73 + 60*x^71 + 20*x^70 + 126*x^69 + 108*x^68 + 108*x^67 + 44*x^66 + 97*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 126*x^5 + 44*x^4 + 44*x^3 + 108*x^2 + 73*x + 20, x^73 + 60*x^71 + 112*x^70 + 70*x^69 + 64*x^68 + 28*x^67 + 48*x^66 + 105*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 70*x^5 + 64*x^4 + 92*x^3 + 48*x^2 + 81*x + 32, x^73 + 60*x^71 + 28*x^70 + 78*x^69 + 20*x^68 + 76*x^67 + 4*x^66 + 49*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 78*x^5 + 84*x^4 + 12*x^3 + 68*x^2 + 25*x + 12, x^73 + 60*x^71 + 32*x^70 + 54*x^69 + 60*x^67 + 96*x^66 + 89*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 54*x^5 + 124*x^3 + 96*x^2 + 65*x, x^73 + 60*x^71 + 56*x^70 + 102*x^69 + 88*x^68 + 28*x^67 + 40*x^66 + 73*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 102*x^5 + 88*x^4 + 92*x^3 + 40*x^2 + 49*x + 72, x^73 + 60*x^71 + 108*x^70 + 126*x^69 + 52*x^68 + 44*x^67 + 84*x^66 + 33*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 126*x^5 + 116*x^4 + 108*x^3 + 20*x^2 + 9*x + 76, x^73 + 60*x^71 + 96*x^70 + 70*x^69 + 112*x^68 + 28*x^67 + 105*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 70*x^5 + 112*x^4 + 92*x^3 + 81*x + 48, x^73 + 60*x^71 + 96*x^70 + 38*x^69 + 112*x^68 + 28*x^67 + 64*x^66 + 9*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 38*x^5 + 112*x^4 + 92*x^3 + 64*x^2 + 113*x + 112, x^73 + 60*x^71 + 22*x^69 + 32*x^68 + 124*x^67 + 57*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 22*x^5 + 32*x^4 + 60*x^3 + 33*x + 96, x^73 + 60*x^71 + 28*x^70 + 78*x^69 + 84*x^68 + 76*x^67 + 4*x^66 + 49*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 78*x^5 + 20*x^4 + 12*x^3 + 68*x^2 + 25*x + 76, x^73 + 60*x^71 + 84*x^70 + 46*x^69 + 28*x^68 + 76*x^67 + 12*x^66 + 81*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 46*x^5 + 92*x^4 + 12*x^3 + 76*x^2 + 57*x + 68, x^73 + 60*x^71 + 52*x^70 + 78*x^69 + 92*x^68 + 12*x^67 + 108*x^66 + 113*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 78*x^5 + 28*x^4 + 76*x^3 + 44*x^2 + 89*x + 68, x^73 + 60*x^71 + 12*x^70 + 30*x^69 + 20*x^68 + 44*x^67 + 116*x^66 + x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 30*x^5 + 84*x^4 + 108*x^3 + 52*x^2 + 105*x + 44, x^73 + 60*x^71 + 38*x^69 + 16*x^68 + 28*x^67 + 32*x^66 + 9*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 38*x^5 + 16*x^4 + 92*x^3 + 32*x^2 + 113*x + 80, x^73 + 60*x^71 + 36*x^70 + 14*x^69 + 76*x^68 + 12*x^67 + 60*x^66 + 49*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 14*x^5 + 12*x^4 + 76*x^3 + 124*x^2 + 25*x + 20, x^73 + 60*x^71 + 112*x^70 + 102*x^69 + 32*x^68 + 92*x^67 + 112*x^66 + 9*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 102*x^5 + 32*x^4 + 28*x^3 + 112*x^2 + 113*x, x^73 + 60*x^71 + 112*x^70 + 118*x^69 + 80*x^68 + 124*x^67 + 16*x^66 + 89*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 118*x^5 + 80*x^4 + 60*x^3 + 16*x^2 + 65*x + 48, x^73 + 60*x^71 + 96*x^70 + 6*x^69 + 16*x^68 + 92*x^67 + 105*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 6*x^5 + 16*x^4 + 28*x^3 + 81*x + 16, x^73 + 60*x^71 + 32*x^70 + 54*x^69 + 96*x^68 + 124*x^67 + 96*x^66 + 25*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 54*x^5 + 96*x^4 + 60*x^3 + 96*x^2 + x + 32, x^73 + 60*x^71 + 96*x^70 + 118*x^69 + 32*x^68 + 60*x^67 + 96*x^66 + 25*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 118*x^5 + 32*x^4 + 124*x^3 + 96*x^2 + x + 32, x^73 + 60*x^71 + 20*x^70 + 14*x^69 + 28*x^68 + 76*x^67 + 12*x^66 + 113*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 14*x^5 + 92*x^4 + 12*x^3 + 76*x^2 + 89*x + 4, x^73 + 60*x^71 + 64*x^70 + 118*x^69 + 32*x^68 + 124*x^67 + 89*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 118*x^5 + 32*x^4 + 60*x^3 + 65*x + 32, x^73 + 60*x^71 + 52*x^70 + 126*x^69 + 12*x^68 + 44*x^67 + 76*x^66 + 33*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 126*x^5 + 76*x^4 + 108*x^3 + 12*x^2 + 9*x + 52, x^73 + 60*x^71 + 68*x^70 + 94*x^69 + 28*x^68 + 44*x^67 + 60*x^66 + 65*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 94*x^5 + 92*x^4 + 108*x^3 + 124*x^2 + 41*x + 36, x^73 + 60*x^71 + 80*x^70 + 6*x^69 + 64*x^68 + 92*x^67 + 80*x^66 + 105*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 6*x^5 + 64*x^4 + 28*x^3 + 80*x^2 + 81*x + 32, x^73 + 60*x^71 + 28*x^70 + 46*x^69 + 84*x^68 + 12*x^67 + 4*x^66 + 17*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 46*x^5 + 20*x^4 + 76*x^3 + 68*x^2 + 121*x + 76, x^73 + 60*x^71 + 68*x^70 + 126*x^69 + 60*x^68 + 108*x^67 + 124*x^66 + 97*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 126*x^5 + 124*x^4 + 44*x^3 + 60*x^2 + 73*x + 68, x^73 + 60*x^71 + 120*x^70 + 38*x^69 + 88*x^68 + 28*x^67 + 104*x^66 + 9*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 38*x^5 + 88*x^4 + 92*x^3 + 104*x^2 + 113*x + 72, x^73 + 60*x^71 + 56*x^70 + 38*x^69 + 120*x^68 + 28*x^67 + 104*x^66 + 9*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 38*x^5 + 120*x^4 + 92*x^3 + 104*x^2 + 113*x + 104, x^73 + 60*x^71 + 12*x^70 + 126*x^69 + 84*x^68 + 108*x^67 + 116*x^66 + 97*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 126*x^5 + 20*x^4 + 44*x^3 + 52*x^2 + 73*x + 108, x^73 + 60*x^71 + 32*x^70 + 38*x^69 + 112*x^68 + 28*x^67 + 9*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 38*x^5 + 112*x^4 + 92*x^3 + 113*x + 112, x^73 + 60*x^71 + 112*x^70 + 38*x^69 + 32*x^68 + 28*x^67 + 48*x^66 + 9*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 38*x^5 + 32*x^4 + 92*x^3 + 48*x^2 + 113*x + 64, x^73 + 60*x^71 + 108*x^70 + 14*x^69 + 68*x^68 + 76*x^67 + 52*x^66 + 113*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 14*x^5 + 4*x^4 + 12*x^3 + 116*x^2 + 89*x + 92, x^73 + 60*x^71 + 96*x^70 + 38*x^69 + 48*x^68 + 28*x^67 + 64*x^66 + 9*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 38*x^5 + 48*x^4 + 92*x^3 + 64*x^2 + 113*x + 48, x^73 + 60*x^71 + 4*x^70 + 30*x^69 + 28*x^68 + 44*x^67 + 124*x^66 + x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 30*x^5 + 92*x^4 + 108*x^3 + 60*x^2 + 105*x + 36, x^73 + 60*x^71 + 4*x^70 + 94*x^69 + 124*x^68 + 108*x^67 + 124*x^66 + x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 94*x^5 + 60*x^4 + 44*x^3 + 60*x^2 + 105*x + 68, x^73 + 60*x^71 + 108*x^70 + 94*x^69 + 84*x^68 + 44*x^67 + 84*x^66 + 65*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 94*x^5 + 20*x^4 + 108*x^3 + 20*x^2 + 41*x + 44, x^73 + 60*x^71 + 4*x^70 + 94*x^69 + 28*x^68 + 108*x^67 + 60*x^66 + x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 94*x^5 + 92*x^4 + 44*x^3 + 124*x^2 + 105*x + 100, x^73 + 60*x^71 + 8*x^70 + 38*x^69 + 104*x^68 + 28*x^67 + 24*x^66 + 9*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 38*x^5 + 104*x^4 + 92*x^3 + 24*x^2 + 113*x + 120, x^73 + 60*x^71 + 36*x^70 + 14*x^69 + 44*x^68 + 76*x^67 + 60*x^66 + 113*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 14*x^5 + 108*x^4 + 12*x^3 + 124*x^2 + 89*x + 52, x^73 + 60*x^71 + 104*x^70 + 22*x^69 + 88*x^68 + 60*x^67 + 88*x^66 + 121*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 22*x^5 + 88*x^4 + 124*x^3 + 88*x^2 + 97*x + 104, x^73 + 60*x^71 + 60*x^70 + 78*x^69 + 52*x^68 + 76*x^67 + 100*x^66 + 49*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 78*x^5 + 116*x^4 + 12*x^3 + 36*x^2 + 25*x + 108, x^73 + 60*x^71 + 80*x^70 + 70*x^69 + 96*x^68 + 92*x^67 + 16*x^66 + 41*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 70*x^5 + 96*x^4 + 28*x^3 + 16*x^2 + 17*x + 64, x^73 + 60*x^71 + 70*x^69 + 16*x^68 + 28*x^67 + 96*x^66 + 105*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 70*x^5 + 16*x^4 + 92*x^3 + 96*x^2 + 81*x + 16, x^73 + 60*x^71 + 48*x^70 + 86*x^69 + 16*x^68 + 60*x^67 + 80*x^66 + 57*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 86*x^5 + 16*x^4 + 124*x^3 + 80*x^2 + 33*x + 112, x^73 + 60*x^71 + 88*x^70 + 102*x^69 + 120*x^68 + 28*x^67 + 8*x^66 + 73*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 102*x^5 + 120*x^4 + 92*x^3 + 8*x^2 + 49*x + 40, x^73 + 60*x^71 + 68*x^70 + 94*x^69 + 124*x^68 + 108*x^67 + 60*x^66 + x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 94*x^5 + 60*x^4 + 44*x^3 + 124*x^2 + 105*x + 68, x^73 + 60*x^71 + 80*x^70 + 54*x^69 + 112*x^68 + 124*x^67 + 48*x^66 + 25*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 54*x^5 + 112*x^4 + 60*x^3 + 48*x^2 + x + 16, x^73 + 60*x^71 + 76*x^70 + 78*x^69 + 4*x^68 + 12*x^67 + 84*x^66 + 113*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 78*x^5 + 68*x^4 + 76*x^3 + 20*x^2 + 89*x + 28, x^73 + 60*x^71 + 100*x^70 + 78*x^69 + 108*x^68 + 76*x^67 + 124*x^66 + 49*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 78*x^5 + 44*x^4 + 12*x^3 + 60*x^2 + 25*x + 116, x^73 + 60*x^71 + 112*x^70 + 70*x^69 + 92*x^67 + 112*x^66 + 41*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 70*x^5 + 28*x^3 + 112*x^2 + 17*x + 32, x^73 + 60*x^71 + 44*x^70 + 78*x^69 + 36*x^68 + 76*x^67 + 52*x^66 + 49*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 78*x^5 + 100*x^4 + 12*x^3 + 116*x^2 + 25*x + 60, x^73 + 60*x^71 + 88*x^70 + 6*x^69 + 88*x^68 + 28*x^67 + 8*x^66 + 41*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 6*x^5 + 88*x^4 + 92*x^3 + 8*x^2 + 17*x + 72, x^73 + 60*x^71 + 24*x^70 + 22*x^69 + 8*x^68 + 124*x^67 + 40*x^66 + 57*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 22*x^5 + 8*x^4 + 60*x^3 + 40*x^2 + 33*x + 56, x^73 + 60*x^71 + 56*x^70 + 6*x^69 + 56*x^68 + 92*x^67 + 104*x^66 + 105*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 6*x^5 + 56*x^4 + 28*x^3 + 104*x^2 + 81*x + 40, x^73 + 60*x^71 + 48*x^70 + 6*x^69 + 64*x^68 + 92*x^67 + 48*x^66 + 105*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 6*x^5 + 64*x^4 + 28*x^3 + 48*x^2 + 81*x + 96, x^73 + 60*x^71 + 56*x^70 + 70*x^69 + 120*x^68 + 28*x^67 + 40*x^66 + 105*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 70*x^5 + 120*x^4 + 92*x^3 + 40*x^2 + 81*x + 40, x^73 + 60*x^71 + 28*x^70 + 46*x^69 + 84*x^68 + 76*x^67 + 68*x^66 + 81*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 46*x^5 + 20*x^4 + 12*x^3 + 4*x^2 + 57*x + 12, x^73 + 60*x^71 + 108*x^70 + 62*x^69 + 116*x^68 + 44*x^67 + 84*x^66 + 97*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 62*x^5 + 52*x^4 + 108*x^3 + 20*x^2 + 73*x + 12, x^73 + 60*x^71 + 64*x^70 + 118*x^69 + 60*x^67 + 25*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 118*x^5 + 124*x^3 + x + 64, x^73 + 60*x^71 + 56*x^70 + 102*x^69 + 24*x^68 + 92*x^67 + 104*x^66 + 9*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 102*x^5 + 24*x^4 + 28*x^3 + 104*x^2 + 113*x + 72, x^73 + 60*x^71 + 104*x^70 + 118*x^69 + 56*x^68 + 60*x^67 + 88*x^66 + 25*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 118*x^5 + 56*x^4 + 124*x^3 + 88*x^2 + x + 8, x^73 + 60*x^71 + 40*x^70 + 102*x^69 + 104*x^68 + 92*x^67 + 120*x^66 + 9*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 102*x^5 + 104*x^4 + 28*x^3 + 120*x^2 + 113*x + 120, x^73 + 60*x^71 + 12*x^70 + 30*x^69 + 116*x^68 + 108*x^67 + 116*x^66 + 65*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 30*x^5 + 52*x^4 + 44*x^3 + 52*x^2 + 41*x + 76, x^73 + 60*x^71 + 100*x^70 + 46*x^69 + 12*x^68 + 76*x^67 + 124*x^66 + 81*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 46*x^5 + 76*x^4 + 12*x^3 + 60*x^2 + 57*x + 84, x^73 + 60*x^71 + 60*x^70 + 14*x^69 + 20*x^68 + 76*x^67 + 36*x^66 + 113*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 14*x^5 + 84*x^4 + 12*x^3 + 100*x^2 + 89*x + 76, x^73 + 60*x^71 + 20*x^70 + 110*x^69 + 28*x^68 + 12*x^67 + 12*x^66 + 81*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 110*x^5 + 92*x^4 + 76*x^3 + 76*x^2 + 57*x + 4, x^73 + 60*x^71 + 84*x^70 + 14*x^69 + 28*x^68 + 12*x^67 + 12*x^66 + 49*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 14*x^5 + 92*x^4 + 76*x^3 + 76*x^2 + 25*x + 68, x^73 + 60*x^71 + 40*x^70 + 38*x^69 + 72*x^68 + 28*x^67 + 120*x^66 + 9*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 38*x^5 + 72*x^4 + 92*x^3 + 120*x^2 + 113*x + 24, x^73 + 60*x^71 + 24*x^70 + 38*x^69 + 120*x^68 + 92*x^67 + 8*x^66 + 73*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 38*x^5 + 120*x^4 + 28*x^3 + 8*x^2 + 49*x + 104, x^73 + 60*x^71 + 12*x^70 + 46*x^69 + 36*x^68 + 12*x^67 + 20*x^66 + 17*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 46*x^5 + 100*x^4 + 76*x^3 + 84*x^2 + 121*x + 124, x^73 + 60*x^71 + 12*x^70 + 30*x^69 + 84*x^68 + 108*x^67 + 52*x^66 + 65*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 30*x^5 + 20*x^4 + 44*x^3 + 116*x^2 + 41*x + 44, x^73 + 60*x^71 + 112*x^70 + 6*x^69 + 96*x^68 + 28*x^67 + 112*x^66 + 41*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 6*x^5 + 96*x^4 + 92*x^3 + 112*x^2 + 17*x + 64, x^73 + 60*x^71 + 72*x^70 + 6*x^69 + 40*x^68 + 28*x^67 + 24*x^66 + 41*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 6*x^5 + 40*x^4 + 92*x^3 + 24*x^2 + 17*x + 120, x^73 + 60*x^71 + 120*x^70 + 38*x^69 + 56*x^68 + 92*x^67 + 104*x^66 + 73*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 38*x^5 + 56*x^4 + 28*x^3 + 104*x^2 + 49*x + 104, x^73 + 60*x^71 + 56*x^70 + 54*x^69 + 104*x^68 + 124*x^67 + 72*x^66 + 25*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 54*x^5 + 104*x^4 + 60*x^3 + 72*x^2 + x + 24, x^73 + 60*x^71 + 16*x^70 + 22*x^69 + 16*x^68 + 124*x^67 + 112*x^66 + 57*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 22*x^5 + 16*x^4 + 60*x^3 + 112*x^2 + 33*x + 112, x^73 + 60*x^71 + 32*x^70 + 38*x^69 + 16*x^68 + 92*x^67 + 73*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 38*x^5 + 16*x^4 + 28*x^3 + 49*x + 80, x^73 + 60*x^71 + 44*x^70 + 78*x^69 + 68*x^68 + 12*x^67 + 52*x^66 + 113*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 78*x^5 + 4*x^4 + 76*x^3 + 116*x^2 + 89*x + 28, x^73 + 60*x^71 + 16*x^70 + 70*x^69 + 92*x^67 + 16*x^66 + 41*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 70*x^5 + 28*x^3 + 16*x^2 + 17*x + 96, x^73 + 60*x^71 + 96*x^70 + 118*x^69 + 32*x^68 + 124*x^67 + 32*x^66 + 89*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 118*x^5 + 32*x^4 + 60*x^3 + 32*x^2 + 65*x + 96, x^73 + 60*x^71 + 88*x^70 + 38*x^69 + 56*x^68 + 92*x^67 + 72*x^66 + 73*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 38*x^5 + 56*x^4 + 28*x^3 + 72*x^2 + 49*x + 40, x^73 + 60*x^71 + 72*x^70 + 6*x^69 + 104*x^68 + 28*x^67 + 24*x^66 + 41*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 6*x^5 + 104*x^4 + 92*x^3 + 24*x^2 + 17*x + 56, x^73 + 60*x^71 + 104*x^70 + 102*x^69 + 104*x^68 + 92*x^67 + 56*x^66 + 9*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 102*x^5 + 104*x^4 + 28*x^3 + 56*x^2 + 113*x + 120, x^73 + 60*x^71 + 116*x^70 + 110*x^69 + 28*x^68 + 12*x^67 + 108*x^66 + 81*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 110*x^5 + 92*x^4 + 76*x^3 + 44*x^2 + 57*x + 68, x^73 + 60*x^71 + 52*x^70 + 30*x^69 + 12*x^68 + 44*x^67 + 12*x^66 + x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 30*x^5 + 76*x^4 + 108*x^3 + 76*x^2 + 105*x + 116, x^73 + 60*x^71 + 84*x^70 + 14*x^69 + 60*x^68 + 12*x^67 + 76*x^66 + 49*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 14*x^5 + 124*x^4 + 76*x^3 + 12*x^2 + 25*x + 100, x^73 + 60*x^71 + 84*x^70 + 94*x^69 + 108*x^68 + 108*x^67 + 44*x^66 + x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 94*x^5 + 44*x^4 + 44*x^3 + 108*x^2 + 105*x + 84, x^73 + 60*x^71 + 92*x^70 + 46*x^69 + 20*x^68 + 76*x^67 + 4*x^66 + 81*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 46*x^5 + 84*x^4 + 12*x^3 + 68*x^2 + 57*x + 76, x^73 + 60*x^71 + 96*x^70 + 118*x^69 + 64*x^68 + 60*x^67 + 32*x^66 + 25*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 118*x^5 + 64*x^4 + 124*x^3 + 32*x^2 + x + 64, x^73 + 60*x^71 + 38*x^69 + 112*x^68 + 92*x^67 + 32*x^66 + 73*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 38*x^5 + 112*x^4 + 28*x^3 + 32*x^2 + 49*x + 112, x^73 + 60*x^71 + 24*x^70 + 70*x^69 + 24*x^68 + 92*x^67 + 8*x^66 + 41*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 70*x^5 + 24*x^4 + 28*x^3 + 8*x^2 + 17*x + 72, x^73 + 60*x^71 + 104*x^70 + 86*x^69 + 88*x^68 + 124*x^67 + 24*x^66 + 121*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 86*x^5 + 88*x^4 + 60*x^3 + 24*x^2 + 97*x + 40, x^73 + 60*x^71 + 12*x^70 + 94*x^69 + 20*x^68 + 44*x^67 + 116*x^66 + 65*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 94*x^5 + 84*x^4 + 108*x^3 + 52*x^2 + 41*x + 44, x^73 + 60*x^71 + 112*x^70 + 70*x^69 + 32*x^68 + 92*x^67 + 48*x^66 + 41*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 70*x^5 + 32*x^4 + 28*x^3 + 48*x^2 + 17*x + 64, x^73 + 60*x^71 + 124*x^70 + 94*x^69 + 100*x^68 + 44*x^67 + 4*x^66 + 65*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 94*x^5 + 36*x^4 + 108*x^3 + 68*x^2 + 41*x + 92, x^73 + 60*x^71 + 64*x^70 + 38*x^69 + 48*x^68 + 92*x^67 + 96*x^66 + 73*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 38*x^5 + 48*x^4 + 28*x^3 + 96*x^2 + 49*x + 48, x^73 + 60*x^71 + 20*x^70 + 46*x^69 + 92*x^68 + 76*x^67 + 76*x^66 + 81*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 46*x^5 + 28*x^4 + 12*x^3 + 12*x^2 + 57*x + 4, x^73 + 60*x^71 + 64*x^70 + 86*x^69 + 32*x^68 + 60*x^67 + 57*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 86*x^5 + 32*x^4 + 124*x^3 + 33*x + 32, x^73 + 60*x^71 + 44*x^70 + 30*x^69 + 84*x^68 + 108*x^67 + 84*x^66 + 65*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 30*x^5 + 20*x^4 + 44*x^3 + 20*x^2 + 41*x + 108, x^73 + 60*x^71 + 28*x^70 + 30*x^69 + 4*x^68 + 108*x^67 + 36*x^66 + 65*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 30*x^5 + 68*x^4 + 44*x^3 + 100*x^2 + 41*x + 124, x^73 + 60*x^71 + 40*x^70 + 54*x^69 + 56*x^68 + 124*x^67 + 88*x^66 + 25*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 54*x^5 + 56*x^4 + 60*x^3 + 88*x^2 + x + 72, x^73 + 60*x^71 + 88*x^70 + 102*x^69 + 56*x^68 + 92*x^67 + 72*x^66 + 9*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 102*x^5 + 56*x^4 + 28*x^3 + 72*x^2 + 113*x + 40, x^73 + 60*x^71 + 84*x^70 + 46*x^69 + 28*x^68 + 12*x^67 + 76*x^66 + 17*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 46*x^5 + 92*x^4 + 76*x^3 + 12*x^2 + 121*x + 4, x^73 + 60*x^71 + 48*x^70 + 54*x^69 + 112*x^68 + 60*x^67 + 80*x^66 + 89*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 54*x^5 + 112*x^4 + 124*x^3 + 80*x^2 + 65*x + 16, x^73 + 60*x^71 + 96*x^70 + 6*x^69 + 80*x^68 + 92*x^67 + 105*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 6*x^5 + 80*x^4 + 28*x^3 + 81*x + 80, x^73 + 60*x^71 + 92*x^70 + 30*x^69 + 4*x^68 + 44*x^67 + 36*x^66 + x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 30*x^5 + 68*x^4 + 108*x^3 + 100*x^2 + 105*x + 60, x^73 + 60*x^71 + 36*x^70 + 94*x^69 + 124*x^68 + 44*x^67 + 92*x^66 + 65*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 94*x^5 + 60*x^4 + 108*x^3 + 28*x^2 + 41*x + 68, x^73 + 60*x^71 + 24*x^70 + 6*x^69 + 88*x^68 + 92*x^67 + 8*x^66 + 105*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 6*x^5 + 88*x^4 + 28*x^3 + 8*x^2 + 81*x + 8, x^73 + 60*x^71 + 64*x^70 + 54*x^69 + 64*x^68 + 124*x^67 + 64*x^66 + 25*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 54*x^5 + 64*x^4 + 60*x^3 + 64*x^2 + x + 64, x^73 + 60*x^71 + 4*x^70 + 126*x^69 + 92*x^68 + 108*x^67 + 124*x^66 + 97*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 126*x^5 + 28*x^4 + 44*x^3 + 60*x^2 + 73*x + 100, x^73 + 60*x^71 + 4*x^70 + 46*x^69 + 76*x^68 + 76*x^67 + 28*x^66 + 81*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 46*x^5 + 12*x^4 + 12*x^3 + 92*x^2 + 57*x + 84, x^73 + 60*x^71 + 44*x^70 + 30*x^69 + 52*x^68 + 44*x^67 + 84*x^66 + x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 30*x^5 + 116*x^4 + 108*x^3 + 20*x^2 + 105*x + 12, x^73 + 60*x^71 + 72*x^70 + 102*x^69 + 104*x^68 + 92*x^67 + 24*x^66 + 9*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 102*x^5 + 104*x^4 + 28*x^3 + 24*x^2 + 113*x + 56, x^73 + 60*x^71 + 36*x^70 + 46*x^69 + 108*x^68 + 12*x^67 + 60*x^66 + 17*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 46*x^5 + 44*x^4 + 76*x^3 + 124*x^2 + 121*x + 116, x^73 + 60*x^71 + 36*x^70 + 30*x^69 + 124*x^68 + 44*x^67 + 92*x^66 + x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 30*x^5 + 60*x^4 + 108*x^3 + 28*x^2 + 105*x + 68, x^73 + 60*x^71 + 116*x^70 + 14*x^69 + 60*x^68 + 12*x^67 + 108*x^66 + 49*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 14*x^5 + 124*x^4 + 76*x^3 + 44*x^2 + 25*x + 36, x^73 + 60*x^71 + 100*x^70 + 46*x^69 + 108*x^68 + 76*x^67 + 60*x^66 + 81*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 46*x^5 + 44*x^4 + 12*x^3 + 124*x^2 + 57*x + 52, x^73 + 60*x^71 + 84*x^70 + 110*x^69 + 92*x^68 + 76*x^67 + 12*x^66 + 17*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 110*x^5 + 28*x^4 + 12*x^3 + 76*x^2 + 121*x + 4, x^73 + 60*x^71 + 24*x^70 + 118*x^69 + 40*x^68 + 60*x^67 + 104*x^66 + 25*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 118*x^5 + 40*x^4 + 124*x^3 + 104*x^2 + x + 88, x^73 + 60*x^71 + 92*x^70 + 110*x^69 + 52*x^68 + 12*x^67 + 4*x^66 + 81*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 110*x^5 + 116*x^4 + 76*x^3 + 68*x^2 + 57*x + 44, x^73 + 60*x^71 + 86*x^69 + 60*x^67 + 57*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 86*x^5 + 124*x^3 + 33*x, x^73 + 60*x^71 + 96*x^70 + 54*x^69 + 64*x^68 + 60*x^67 + 32*x^66 + 89*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 54*x^5 + 64*x^4 + 124*x^3 + 32*x^2 + 65*x + 64, x^73 + 60*x^71 + 124*x^70 + 110*x^69 + 52*x^68 + 12*x^67 + 36*x^66 + 81*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 110*x^5 + 116*x^4 + 76*x^3 + 100*x^2 + 57*x + 108, x^73 + 60*x^71 + 70*x^69 + 80*x^68 + 28*x^67 + 96*x^66 + 105*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 70*x^5 + 80*x^4 + 92*x^3 + 96*x^2 + 81*x + 80, x^73 + 60*x^71 + 52*x^70 + 126*x^69 + 108*x^68 + 44*x^67 + 12*x^66 + 33*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 126*x^5 + 44*x^4 + 108*x^3 + 76*x^2 + 9*x + 20, x^73 + 60*x^71 + 12*x^70 + 46*x^69 + 100*x^68 + 76*x^67 + 84*x^66 + 81*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 46*x^5 + 36*x^4 + 12*x^3 + 20*x^2 + 57*x + 124, x^73 + 60*x^71 + 88*x^70 + 70*x^69 + 88*x^68 + 92*x^67 + 72*x^66 + 41*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 70*x^5 + 88*x^4 + 28*x^3 + 72*x^2 + 17*x + 8, x^73 + 60*x^71 + 32*x^70 + 86*x^69 + 96*x^68 + 124*x^67 + 32*x^66 + 121*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 86*x^5 + 96*x^4 + 60*x^3 + 32*x^2 + 97*x + 96, x^73 + 60*x^71 + 4*x^70 + 62*x^69 + 124*x^68 + 108*x^67 + 60*x^66 + 33*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 62*x^5 + 60*x^4 + 44*x^3 + 124*x^2 + 9*x + 4, x^73 + 60*x^71 + 20*x^70 + 78*x^69 + 28*x^68 + 76*x^67 + 12*x^66 + 49*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 78*x^5 + 92*x^4 + 12*x^3 + 76*x^2 + 25*x + 4, x^73 + 60*x^71 + 32*x^70 + 118*x^69 + 124*x^67 + 32*x^66 + 89*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 118*x^5 + 60*x^3 + 32*x^2 + 65*x + 64, x^73 + 60*x^71 + 88*x^70 + 70*x^69 + 24*x^68 + 92*x^67 + 72*x^66 + 41*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 70*x^5 + 24*x^4 + 28*x^3 + 72*x^2 + 17*x + 72, x^73 + 60*x^71 + 12*x^70 + 30*x^69 + 84*x^68 + 44*x^67 + 116*x^66 + x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 30*x^5 + 20*x^4 + 108*x^3 + 52*x^2 + 105*x + 108, x^73 + 60*x^71 + 40*x^70 + 6*x^69 + 40*x^68 + 92*x^67 + 56*x^66 + 105*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 6*x^5 + 40*x^4 + 28*x^3 + 56*x^2 + 81*x + 120, x^73 + 60*x^71 + 48*x^70 + 86*x^69 + 48*x^68 + 124*x^67 + 80*x^66 + 121*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 86*x^5 + 48*x^4 + 60*x^3 + 80*x^2 + 97*x + 80, x^73 + 60*x^71 + 4*x^70 + 78*x^69 + 76*x^68 + 12*x^67 + 28*x^66 + 113*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 78*x^5 + 12*x^4 + 76*x^3 + 92*x^2 + 89*x + 84, x^73 + 60*x^71 + 120*x^70 + 6*x^69 + 24*x^68 + 28*x^67 + 40*x^66 + 41*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 6*x^5 + 24*x^4 + 92*x^3 + 40*x^2 + 17*x + 72, x^73 + 60*x^71 + 76*x^70 + 62*x^69 + 116*x^68 + 108*x^67 + 116*x^66 + 33*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 62*x^5 + 52*x^4 + 44*x^3 + 52*x^2 + 9*x + 12, x^73 + 60*x^71 + 36*x^70 + 46*x^69 + 108*x^68 + 76*x^67 + 124*x^66 + 81*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 46*x^5 + 44*x^4 + 12*x^3 + 60*x^2 + 57*x + 52, x^73 + 60*x^71 + 76*x^70 + 62*x^69 + 84*x^68 + 108*x^67 + 52*x^66 + 33*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 62*x^5 + 20*x^4 + 44*x^3 + 116*x^2 + 9*x + 108, x^73 + 60*x^71 + 72*x^70 + 118*x^69 + 88*x^68 + 60*x^67 + 120*x^66 + 25*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 118*x^5 + 88*x^4 + 124*x^3 + 120*x^2 + x + 104, x^73 + 60*x^71 + 56*x^70 + 70*x^69 + 24*x^68 + 28*x^67 + 104*x^66 + 105*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 70*x^5 + 24*x^4 + 92*x^3 + 104*x^2 + 81*x + 72, x^73 + 60*x^71 + 16*x^70 + 22*x^69 + 48*x^68 + 124*x^67 + 48*x^66 + 57*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 22*x^5 + 48*x^4 + 60*x^3 + 48*x^2 + 33*x + 16, x^73 + 60*x^71 + 40*x^70 + 70*x^69 + 104*x^68 + 28*x^67 + 120*x^66 + 105*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 70*x^5 + 104*x^4 + 92*x^3 + 120*x^2 + 81*x + 120, x^73 + 60*x^71 + 84*x^70 + 78*x^69 + 28*x^68 + 12*x^67 + 12*x^66 + 113*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 78*x^5 + 92*x^4 + 76*x^3 + 76*x^2 + 89*x + 68, x^73 + 60*x^71 + 52*x^70 + 110*x^69 + 60*x^68 + 12*x^67 + 108*x^66 + 81*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 110*x^5 + 124*x^4 + 76*x^3 + 44*x^2 + 57*x + 100, x^73 + 60*x^71 + 60*x^70 + 46*x^69 + 52*x^68 + 12*x^67 + 100*x^66 + 17*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 46*x^5 + 116*x^4 + 76*x^3 + 36*x^2 + 121*x + 108, x^73 + 60*x^71 + 60*x^70 + 126*x^69 + 68*x^68 + 44*x^67 + 68*x^66 + 33*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 126*x^5 + 4*x^4 + 108*x^3 + 4*x^2 + 9*x + 124, x^73 + 60*x^71 + 92*x^70 + 14*x^69 + 84*x^68 + 76*x^67 + 68*x^66 + 113*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 14*x^5 + 20*x^4 + 12*x^3 + 4*x^2 + 89*x + 76, x^73 + 60*x^71 + 88*x^70 + 54*x^69 + 72*x^68 + 124*x^67 + 40*x^66 + 25*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 54*x^5 + 72*x^4 + 60*x^3 + 40*x^2 + x + 56, x^73 + 60*x^71 + 8*x^70 + 54*x^69 + 120*x^68 + 124*x^67 + 56*x^66 + 25*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 54*x^5 + 120*x^4 + 60*x^3 + 56*x^2 + x + 72, x^73 + 60*x^71 + 64*x^70 + 54*x^69 + 32*x^68 + 60*x^67 + 64*x^66 + 89*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 54*x^5 + 32*x^4 + 124*x^3 + 64*x^2 + 65*x + 96, x^73 + 60*x^71 + 16*x^70 + 118*x^69 + 16*x^68 + 124*x^67 + 48*x^66 + 89*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 118*x^5 + 16*x^4 + 60*x^3 + 48*x^2 + 65*x + 48, x^73 + 60*x^71 + 20*x^70 + 30*x^69 + 44*x^68 + 44*x^67 + 44*x^66 + x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 30*x^5 + 108*x^4 + 108*x^3 + 108*x^2 + 105*x + 84, x^73 + 60*x^71 + 88*x^70 + 86*x^69 + 8*x^68 + 60*x^67 + 40*x^66 + 57*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 86*x^5 + 8*x^4 + 124*x^3 + 40*x^2 + 33*x + 120, x^73 + 60*x^71 + 48*x^70 + 70*x^69 + 64*x^68 + 28*x^67 + 112*x^66 + 105*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 70*x^5 + 64*x^4 + 92*x^3 + 112*x^2 + 81*x + 32, x^73 + 60*x^71 + 116*x^70 + 14*x^69 + 28*x^68 + 76*x^67 + 108*x^66 + 113*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 14*x^5 + 92*x^4 + 12*x^3 + 44*x^2 + 89*x + 68, x^73 + 60*x^71 + 92*x^70 + 126*x^69 + 36*x^68 + 108*x^67 + 100*x^66 + 97*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 126*x^5 + 100*x^4 + 44*x^3 + 36*x^2 + 73*x + 92, x^73 + 60*x^71 + 80*x^70 + 22*x^69 + 80*x^68 + 124*x^67 + 48*x^66 + 57*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 22*x^5 + 80*x^4 + 60*x^3 + 48*x^2 + 33*x + 48, x^73 + 60*x^71 + 56*x^70 + 54*x^69 + 8*x^68 + 60*x^67 + 72*x^66 + 89*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 54*x^5 + 8*x^4 + 124*x^3 + 72*x^2 + 65*x + 120, x^73 + 60*x^71 + 8*x^70 + 70*x^69 + 104*x^68 + 92*x^67 + 24*x^66 + 41*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 70*x^5 + 104*x^4 + 28*x^3 + 24*x^2 + 17*x + 120, x^73 + 60*x^71 + 100*x^70 + 62*x^69 + 92*x^68 + 108*x^67 + 92*x^66 + 33*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 62*x^5 + 28*x^4 + 44*x^3 + 28*x^2 + 9*x + 36, x^73 + 60*x^71 + 20*x^70 + 46*x^69 + 28*x^68 + 12*x^67 + 12*x^66 + 17*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 46*x^5 + 92*x^4 + 76*x^3 + 76*x^2 + 121*x + 4, x^73 + 60*x^71 + 92*x^70 + 62*x^69 + 68*x^68 + 108*x^67 + 36*x^66 + 33*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 62*x^5 + 4*x^4 + 44*x^3 + 100*x^2 + 9*x + 124, x^73 + 60*x^71 + 20*x^70 + 126*x^69 + 44*x^68 + 108*x^67 + 44*x^66 + 97*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 126*x^5 + 108*x^4 + 44*x^3 + 108*x^2 + 73*x + 84, x^73 + 60*x^71 + 28*x^70 + 78*x^69 + 20*x^68 + 12*x^67 + 68*x^66 + 113*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 78*x^5 + 84*x^4 + 76*x^3 + 4*x^2 + 89*x + 76, x^73 + 60*x^71 + 64*x^70 + 6*x^69 + 48*x^68 + 92*x^67 + 32*x^66 + 105*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 6*x^5 + 48*x^4 + 28*x^3 + 32*x^2 + 81*x + 112, x^73 + 60*x^71 + 112*x^70 + 6*x^69 + 64*x^68 + 28*x^67 + 48*x^66 + 41*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 6*x^5 + 64*x^4 + 92*x^3 + 48*x^2 + 17*x + 32, x^73 + 60*x^71 + 84*x^70 + 62*x^69 + 12*x^68 + 44*x^67 + 108*x^66 + 97*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 62*x^5 + 76*x^4 + 108*x^3 + 44*x^2 + 73*x + 116, x^73 + 60*x^71 + 124*x^70 + 46*x^69 + 84*x^68 + 76*x^67 + 36*x^66 + 81*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 46*x^5 + 20*x^4 + 12*x^3 + 100*x^2 + 57*x + 76, x^73 + 60*x^71 + 16*x^70 + 6*x^69 + 32*x^68 + 92*x^67 + 80*x^66 + 105*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 6*x^5 + 32*x^4 + 28*x^3 + 80*x^2 + 81*x, x^73 + 60*x^71 + 100*x^70 + 78*x^69 + 12*x^68 + 76*x^67 + 60*x^66 + 49*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 78*x^5 + 76*x^4 + 12*x^3 + 124*x^2 + 25*x + 20, x^73 + 60*x^71 + 36*x^70 + 110*x^69 + 12*x^68 + 76*x^67 + 60*x^66 + 17*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 110*x^5 + 76*x^4 + 12*x^3 + 124*x^2 + 121*x + 84, x^73 + 60*x^71 + 40*x^70 + 6*x^69 + 72*x^68 + 92*x^67 + 120*x^66 + 105*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 6*x^5 + 72*x^4 + 28*x^3 + 120*x^2 + 81*x + 24, x^73 + 60*x^71 + 100*x^70 + 110*x^69 + 44*x^68 + 76*x^67 + 60*x^66 + 17*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 110*x^5 + 108*x^4 + 12*x^3 + 124*x^2 + 121*x + 116, x^73 + 60*x^71 + 24*x^70 + 86*x^69 + 40*x^68 + 124*x^67 + 104*x^66 + 121*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 86*x^5 + 40*x^4 + 60*x^3 + 104*x^2 + 97*x + 88, x^73 + 60*x^71 + 44*x^70 + 30*x^69 + 20*x^68 + 108*x^67 + 84*x^66 + 65*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 30*x^5 + 84*x^4 + 44*x^3 + 20*x^2 + 41*x + 44, x^73 + 60*x^71 + 56*x^70 + 22*x^69 + 40*x^68 + 60*x^67 + 72*x^66 + 121*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 22*x^5 + 40*x^4 + 124*x^3 + 72*x^2 + 97*x + 88, x^73 + 60*x^71 + 60*x^70 + 110*x^69 + 52*x^68 + 12*x^67 + 100*x^66 + 81*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 110*x^5 + 116*x^4 + 76*x^3 + 36*x^2 + 57*x + 108, x^73 + 60*x^71 + 48*x^70 + 70*x^69 + 96*x^68 + 28*x^67 + 48*x^66 + 105*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 70*x^5 + 96*x^4 + 92*x^3 + 48*x^2 + 81*x + 64, x^73 + 60*x^71 + 64*x^70 + 118*x^69 + 96*x^68 + 60*x^67 + 64*x^66 + 25*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 118*x^5 + 96*x^4 + 124*x^3 + 64*x^2 + x + 32, x^73 + 60*x^71 + 92*x^70 + 110*x^69 + 84*x^68 + 76*x^67 + 4*x^66 + 17*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 110*x^5 + 20*x^4 + 12*x^3 + 68*x^2 + 121*x + 12, x^73 + 60*x^71 + 56*x^70 + 22*x^69 + 104*x^68 + 60*x^67 + 72*x^66 + 121*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 22*x^5 + 104*x^4 + 124*x^3 + 72*x^2 + 97*x + 24, x^73 + 60*x^71 + 116*x^70 + 126*x^69 + 108*x^68 + 44*x^67 + 76*x^66 + 33*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 126*x^5 + 44*x^4 + 108*x^3 + 12*x^2 + 9*x + 20, x^73 + 60*x^71 + 112*x^70 + 54*x^69 + 112*x^68 + 124*x^67 + 80*x^66 + 25*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 54*x^5 + 112*x^4 + 60*x^3 + 80*x^2 + x + 80, x^73 + 60*x^71 + 48*x^70 + 86*x^69 + 80*x^68 + 124*x^67 + 16*x^66 + 121*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 86*x^5 + 80*x^4 + 60*x^3 + 16*x^2 + 97*x + 112, x^73 + 60*x^71 + 48*x^70 + 6*x^69 + 28*x^67 + 112*x^66 + 41*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 6*x^5 + 92*x^3 + 112*x^2 + 17*x + 96, x^73 + 60*x^71 + 16*x^70 + 70*x^69 + 28*x^67 + 80*x^66 + 105*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 70*x^5 + 92*x^3 + 80*x^2 + 81*x + 32, x^73 + 60*x^71 + 44*x^70 + 110*x^69 + 36*x^68 + 12*x^67 + 52*x^66 + 81*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 110*x^5 + 100*x^4 + 76*x^3 + 116*x^2 + 57*x + 60, x^73 + 60*x^71 + 22*x^69 + 124*x^67 + 64*x^66 + 57*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 22*x^5 + 60*x^3 + 64*x^2 + 33*x + 64, x^73 + 60*x^71 + 24*x^70 + 22*x^69 + 72*x^68 + 124*x^67 + 40*x^66 + 57*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 22*x^5 + 72*x^4 + 60*x^3 + 40*x^2 + 33*x + 120, x^73 + 60*x^71 + 4*x^70 + 94*x^69 + 92*x^68 + 108*x^67 + 60*x^66 + x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 94*x^5 + 28*x^4 + 44*x^3 + 124*x^2 + 105*x + 36, x^73 + 60*x^71 + 116*x^70 + 110*x^69 + 92*x^68 + 76*x^67 + 44*x^66 + 17*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 110*x^5 + 28*x^4 + 12*x^3 + 108*x^2 + 121*x + 68, x^73 + 60*x^71 + 100*x^70 + 110*x^69 + 44*x^68 + 12*x^67 + 124*x^66 + 81*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 110*x^5 + 108*x^4 + 76*x^3 + 60*x^2 + 57*x + 52, x^73 + 60*x^71 + 4*x^70 + 46*x^69 + 44*x^68 + 76*x^67 + 92*x^66 + 81*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 46*x^5 + 108*x^4 + 12*x^3 + 28*x^2 + 57*x + 52, x^73 + 60*x^71 + 16*x^70 + 70*x^69 + 64*x^68 + 28*x^67 + 80*x^66 + 105*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 70*x^5 + 64*x^4 + 92*x^3 + 80*x^2 + 81*x + 96, x^73 + 60*x^71 + 28*x^70 + 78*x^69 + 84*x^68 + 12*x^67 + 68*x^66 + 113*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 78*x^5 + 20*x^4 + 76*x^3 + 4*x^2 + 89*x + 12, x^73 + 60*x^71 + 68*x^70 + 62*x^69 + 124*x^68 + 44*x^67 + 60*x^66 + 97*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 62*x^5 + 60*x^4 + 108*x^3 + 124*x^2 + 73*x + 68, x^73 + 60*x^71 + 36*x^70 + 46*x^69 + 44*x^68 + 12*x^67 + 60*x^66 + 17*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 46*x^5 + 108*x^4 + 76*x^3 + 124*x^2 + 121*x + 52, x^73 + 60*x^71 + 84*x^70 + 14*x^69 + 124*x^68 + 12*x^67 + 76*x^66 + 49*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 14*x^5 + 60*x^4 + 76*x^3 + 12*x^2 + 25*x + 36, x^73 + 60*x^71 + 72*x^70 + 70*x^69 + 104*x^68 + 28*x^67 + 24*x^66 + 105*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 70*x^5 + 104*x^4 + 92*x^3 + 24*x^2 + 81*x + 56, x^73 + 60*x^71 + 92*x^70 + 14*x^69 + 52*x^68 + 12*x^67 + 68*x^66 + 49*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 14*x^5 + 116*x^4 + 76*x^3 + 4*x^2 + 25*x + 108, x^73 + 60*x^71 + 22*x^69 + 96*x^68 + 124*x^67 + 57*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 22*x^5 + 96*x^4 + 60*x^3 + 33*x + 32, x^73 + 60*x^71 + 24*x^70 + 118*x^69 + 72*x^68 + 60*x^67 + 40*x^66 + 25*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 118*x^5 + 72*x^4 + 124*x^3 + 40*x^2 + x + 120, x^73 + 60*x^71 + 124*x^70 + 30*x^69 + 36*x^68 + 44*x^67 + 4*x^66 + x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 30*x^5 + 100*x^4 + 108*x^3 + 68*x^2 + 105*x + 28, x^73 + 60*x^71 + 64*x^70 + 102*x^69 + 48*x^68 + 28*x^67 + 32*x^66 + 73*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 102*x^5 + 48*x^4 + 92*x^3 + 32*x^2 + 49*x + 112, x^73 + 60*x^71 + 32*x^70 + 102*x^69 + 48*x^68 + 92*x^67 + 64*x^66 + 9*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 102*x^5 + 48*x^4 + 28*x^3 + 64*x^2 + 113*x + 112, x^73 + 60*x^71 + 84*x^70 + 30*x^69 + 108*x^68 + 108*x^67 + 44*x^66 + 65*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 30*x^5 + 44*x^4 + 44*x^3 + 108*x^2 + 41*x + 84, x^73 + 60*x^71 + 116*x^70 + 78*x^69 + 124*x^68 + 12*x^67 + 108*x^66 + 113*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 78*x^5 + 60*x^4 + 76*x^3 + 44*x^2 + 89*x + 100, x^73 + 60*x^71 + 20*x^70 + 78*x^69 + 28*x^68 + 12*x^67 + 76*x^66 + 113*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 78*x^5 + 92*x^4 + 76*x^3 + 12*x^2 + 89*x + 68, x^73 + 60*x^71 + 24*x^70 + 22*x^69 + 72*x^68 + 60*x^67 + 104*x^66 + 121*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 22*x^5 + 72*x^4 + 124*x^3 + 104*x^2 + 97*x + 56, x^73 + 60*x^71 + 100*x^70 + 30*x^69 + 28*x^68 + 108*x^67 + 28*x^66 + 65*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 30*x^5 + 92*x^4 + 44*x^3 + 92*x^2 + 41*x + 36, x^73 + 60*x^71 + 12*x^70 + 62*x^69 + 20*x^68 + 44*x^67 + 52*x^66 + 97*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 62*x^5 + 84*x^4 + 108*x^3 + 116*x^2 + 73*x + 108, x^73 + 60*x^71 + 120*x^70 + 54*x^69 + 8*x^68 + 124*x^67 + 72*x^66 + 25*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 54*x^5 + 8*x^4 + 60*x^3 + 72*x^2 + x + 56, x^73 + 60*x^71 + 92*x^70 + 14*x^69 + 52*x^68 + 76*x^67 + 4*x^66 + 113*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 14*x^5 + 116*x^4 + 12*x^3 + 68*x^2 + 89*x + 44, x^73 + 60*x^71 + 104*x^70 + 70*x^69 + 104*x^68 + 92*x^67 + 120*x^66 + 41*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 70*x^5 + 104*x^4 + 28*x^3 + 120*x^2 + 17*x + 56, x^73 + 60*x^71 + 20*x^70 + 30*x^69 + 108*x^68 + 108*x^67 + 108*x^66 + 65*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 30*x^5 + 44*x^4 + 44*x^3 + 44*x^2 + 41*x + 84, x^73 + 60*x^71 + 12*x^70 + 78*x^69 + 36*x^68 + 76*x^67 + 20*x^66 + 49*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 78*x^5 + 100*x^4 + 12*x^3 + 84*x^2 + 25*x + 124, x^73 + 60*x^71 + 60*x^70 + 30*x^69 + 36*x^68 + 108*x^67 + 4*x^66 + 65*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 30*x^5 + 100*x^4 + 44*x^3 + 68*x^2 + 41*x + 92, x^73 + 60*x^71 + 8*x^70 + 118*x^69 + 56*x^68 + 60*x^67 + 120*x^66 + 25*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 118*x^5 + 56*x^4 + 124*x^3 + 120*x^2 + x + 72, x^73 + 60*x^71 + 86*x^69 + 32*x^68 + 60*x^67 + 64*x^66 + 57*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 86*x^5 + 32*x^4 + 124*x^3 + 64*x^2 + 33*x + 32, x^73 + 60*x^71 + 60*x^70 + 30*x^69 + 4*x^68 + 108*x^67 + 68*x^66 + 65*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 30*x^5 + 68*x^4 + 44*x^3 + 4*x^2 + 41*x + 60, x^73 + 60*x^71 + 36*x^70 + 30*x^69 + 92*x^68 + 108*x^67 + 92*x^66 + 65*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 30*x^5 + 28*x^4 + 44*x^3 + 28*x^2 + 41*x + 100, x^73 + 60*x^71 + 64*x^70 + 38*x^69 + 16*x^68 + 28*x^67 + 96*x^66 + 9*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 38*x^5 + 16*x^4 + 92*x^3 + 96*x^2 + 113*x + 80, x^73 + 60*x^71 + 84*x^70 + 78*x^69 + 124*x^68 + 12*x^67 + 76*x^66 + 113*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 78*x^5 + 60*x^4 + 76*x^3 + 12*x^2 + 89*x + 36, x^73 + 60*x^71 + 12*x^70 + 78*x^69 + 100*x^68 + 76*x^67 + 20*x^66 + 49*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 78*x^5 + 36*x^4 + 12*x^3 + 84*x^2 + 25*x + 60, x^73 + 60*x^71 + 116*x^70 + 46*x^69 + 124*x^68 + 76*x^67 + 108*x^66 + 81*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 46*x^5 + 60*x^4 + 12*x^3 + 44*x^2 + 57*x + 100, x^73 + 60*x^71 + 100*x^70 + 110*x^69 + 12*x^68 + 76*x^67 + 124*x^66 + 17*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 110*x^5 + 76*x^4 + 12*x^3 + 60*x^2 + 121*x + 84, x^73 + 60*x^71 + 120*x^70 + 6*x^69 + 56*x^68 + 92*x^67 + 40*x^66 + 105*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 6*x^5 + 56*x^4 + 28*x^3 + 40*x^2 + 81*x + 40, x^73 + 60*x^71 + 108*x^70 + 30*x^69 + 116*x^68 + 108*x^67 + 84*x^66 + 65*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 30*x^5 + 52*x^4 + 44*x^3 + 20*x^2 + 41*x + 12, x^73 + 60*x^71 + 20*x^70 + 62*x^69 + 12*x^68 + 44*x^67 + 44*x^66 + 97*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 62*x^5 + 76*x^4 + 108*x^3 + 108*x^2 + 73*x + 116, x^73 + 60*x^71 + 104*x^70 + 70*x^69 + 8*x^68 + 28*x^67 + 120*x^66 + 105*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 70*x^5 + 8*x^4 + 92*x^3 + 120*x^2 + 81*x + 24, x^73 + 60*x^71 + 48*x^70 + 22*x^69 + 48*x^68 + 124*x^67 + 80*x^66 + 57*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 22*x^5 + 48*x^4 + 60*x^3 + 80*x^2 + 33*x + 80, x^73 + 60*x^71 + 116*x^70 + 30*x^69 + 12*x^68 + 44*x^67 + 76*x^66 + x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 30*x^5 + 76*x^4 + 108*x^3 + 12*x^2 + 105*x + 116, x^73 + 60*x^71 + 64*x^70 + 102*x^69 + 112*x^68 + 28*x^67 + 32*x^66 + 73*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 102*x^5 + 112*x^4 + 92*x^3 + 32*x^2 + 49*x + 48, x^73 + 60*x^71 + 32*x^70 + 102*x^69 + 112*x^68 + 92*x^67 + 64*x^66 + 9*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 102*x^5 + 112*x^4 + 28*x^3 + 64*x^2 + 113*x + 48, x^73 + 60*x^71 + 116*x^70 + 94*x^69 + 44*x^68 + 44*x^67 + 12*x^66 + 65*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 94*x^5 + 108*x^4 + 108*x^3 + 76*x^2 + 41*x + 20, x^73 + 60*x^71 + 116*x^70 + 14*x^69 + 92*x^68 + 76*x^67 + 108*x^66 + 113*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 14*x^5 + 28*x^4 + 12*x^3 + 44*x^2 + 89*x + 4, x^73 + 60*x^71 + 80*x^70 + 22*x^69 + 112*x^68 + 124*x^67 + 112*x^66 + 57*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 22*x^5 + 112*x^4 + 60*x^3 + 112*x^2 + 33*x + 80, x^73 + 60*x^71 + 100*x^70 + 110*x^69 + 12*x^68 + 12*x^67 + 60*x^66 + 81*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 110*x^5 + 76*x^4 + 76*x^3 + 124*x^2 + 57*x + 20, x^73 + 60*x^71 + 28*x^70 + 46*x^69 + 20*x^68 + 76*x^67 + 68*x^66 + 81*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 46*x^5 + 84*x^4 + 12*x^3 + 4*x^2 + 57*x + 76, x^73 + 60*x^71 + 100*x^70 + 30*x^69 + 124*x^68 + 44*x^67 + 28*x^66 + x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 30*x^5 + 60*x^4 + 108*x^3 + 92*x^2 + 105*x + 68, x^73 + 60*x^71 + 60*x^70 + 110*x^69 + 116*x^68 + 76*x^67 + 36*x^66 + 17*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 110*x^5 + 52*x^4 + 12*x^3 + 100*x^2 + 121*x + 108, x^73 + 60*x^71 + 48*x^70 + 38*x^69 + 32*x^68 + 28*x^67 + 112*x^66 + 9*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 38*x^5 + 32*x^4 + 92*x^3 + 112*x^2 + 113*x + 64, x^73 + 60*x^71 + 8*x^70 + 22*x^69 + 88*x^68 + 124*x^67 + 56*x^66 + 57*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 22*x^5 + 88*x^4 + 60*x^3 + 56*x^2 + 33*x + 104, x^73 + 60*x^71 + 20*x^70 + 30*x^69 + 44*x^68 + 108*x^67 + 108*x^66 + 65*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 30*x^5 + 108*x^4 + 44*x^3 + 44*x^2 + 41*x + 20, x^73 + 60*x^71 + 92*x^70 + 62*x^69 + 100*x^68 + 108*x^67 + 100*x^66 + 33*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 62*x^5 + 36*x^4 + 44*x^3 + 36*x^2 + 9*x + 28, x^73 + 60*x^71 + 16*x^70 + 102*x^69 + 96*x^68 + 92*x^67 + 16*x^66 + 9*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 102*x^5 + 96*x^4 + 28*x^3 + 16*x^2 + 113*x, x^73 + 60*x^71 + 44*x^70 + 14*x^69 + 36*x^68 + 76*x^67 + 52*x^66 + 113*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 14*x^5 + 100*x^4 + 12*x^3 + 116*x^2 + 89*x + 60, x^73 + 60*x^71 + 68*x^70 + 62*x^69 + 124*x^68 + 108*x^67 + 124*x^66 + 33*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 62*x^5 + 60*x^4 + 44*x^3 + 60*x^2 + 9*x + 4, x^73 + 60*x^71 + 108*x^70 + 110*x^69 + 100*x^68 + 76*x^67 + 52*x^66 + 17*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 110*x^5 + 36*x^4 + 12*x^3 + 116*x^2 + 121*x + 60, x^73 + 60*x^71 + 116*x^70 + 30*x^69 + 44*x^68 + 44*x^67 + 12*x^66 + x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 30*x^5 + 108*x^4 + 108*x^3 + 76*x^2 + 105*x + 20, x^73 + 60*x^71 + 80*x^70 + 118*x^69 + 112*x^68 + 60*x^67 + 112*x^66 + 25*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 118*x^5 + 112*x^4 + 124*x^3 + 112*x^2 + x + 80, x^73 + 60*x^71 + 64*x^70 + 38*x^69 + 80*x^68 + 28*x^67 + 96*x^66 + 9*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 38*x^5 + 80*x^4 + 92*x^3 + 96*x^2 + 113*x + 16, x^73 + 60*x^71 + 104*x^70 + 6*x^69 + 40*x^68 + 28*x^67 + 56*x^66 + 41*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 6*x^5 + 40*x^4 + 92*x^3 + 56*x^2 + 17*x + 56, x^73 + 60*x^71 + 120*x^70 + 102*x^69 + 24*x^68 + 28*x^67 + 104*x^66 + 73*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 102*x^5 + 24*x^4 + 92*x^3 + 104*x^2 + 49*x + 8, x^73 + 60*x^71 + 92*x^70 + 78*x^69 + 84*x^68 + 12*x^67 + 4*x^66 + 113*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 78*x^5 + 20*x^4 + 76*x^3 + 68*x^2 + 89*x + 12, x^73 + 60*x^71 + 32*x^70 + 54*x^69 + 64*x^68 + 60*x^67 + 96*x^66 + 89*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 54*x^5 + 64*x^4 + 124*x^3 + 96*x^2 + 65*x + 64, x^73 + 60*x^71 + 36*x^70 + 78*x^69 + 44*x^68 + 12*x^67 + 124*x^66 + 113*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 78*x^5 + 108*x^4 + 76*x^3 + 60*x^2 + 89*x + 116, x^73 + 60*x^71 + 20*x^70 + 62*x^69 + 44*x^68 + 44*x^67 + 108*x^66 + 97*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 62*x^5 + 108*x^4 + 108*x^3 + 44*x^2 + 73*x + 20, x^73 + 60*x^71 + 24*x^70 + 22*x^69 + 40*x^68 + 60*x^67 + 40*x^66 + 121*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 22*x^5 + 40*x^4 + 124*x^3 + 40*x^2 + 97*x + 24, x^73 + 60*x^71 + 28*x^70 + 14*x^69 + 116*x^68 + 76*x^67 + 68*x^66 + 113*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 14*x^5 + 52*x^4 + 12*x^3 + 4*x^2 + 89*x + 108, x^73 + 60*x^71 + 96*x^70 + 38*x^69 + 16*x^68 + 92*x^67 + 64*x^66 + 73*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 38*x^5 + 16*x^4 + 28*x^3 + 64*x^2 + 49*x + 80, x^73 + 60*x^71 + 84*x^70 + 30*x^69 + 76*x^68 + 44*x^67 + 44*x^66 + x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 30*x^5 + 12*x^4 + 108*x^3 + 108*x^2 + 105*x + 116, x^73 + 60*x^71 + 92*x^70 + 30*x^69 + 100*x^68 + 44*x^67 + 100*x^66 + x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 30*x^5 + 36*x^4 + 108*x^3 + 36*x^2 + 105*x + 28, x^73 + 60*x^71 + 120*x^70 + 22*x^69 + 72*x^68 + 124*x^67 + 8*x^66 + 57*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 22*x^5 + 72*x^4 + 60*x^3 + 8*x^2 + 33*x + 56, x^73 + 60*x^71 + 8*x^70 + 6*x^69 + 8*x^68 + 92*x^67 + 88*x^66 + 105*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 6*x^5 + 8*x^4 + 28*x^3 + 88*x^2 + 81*x + 24, x^73 + 60*x^71 + 68*x^70 + 126*x^69 + 92*x^68 + 108*x^67 + 60*x^66 + 97*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 126*x^5 + 28*x^4 + 44*x^3 + 124*x^2 + 73*x + 100, x^73 + 60*x^71 + 118*x^69 + 124*x^67 + 89*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 118*x^5 + 60*x^3 + 65*x, x^73 + 60*x^71 + 64*x^70 + 22*x^69 + 124*x^67 + 57*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 22*x^5 + 60*x^3 + 33*x + 64, x^73 + 60*x^71 + 16*x^70 + 6*x^69 + 96*x^68 + 92*x^67 + 80*x^66 + 105*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 6*x^5 + 96*x^4 + 28*x^3 + 80*x^2 + 81*x + 64, x^73 + 60*x^71 + 40*x^70 + 70*x^69 + 72*x^68 + 92*x^67 + 120*x^66 + 41*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 70*x^5 + 72*x^4 + 28*x^3 + 120*x^2 + 17*x + 24, x^73 + 60*x^71 + 36*x^70 + 14*x^69 + 12*x^68 + 76*x^67 + 124*x^66 + 113*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 14*x^5 + 76*x^4 + 12*x^3 + 60*x^2 + 89*x + 20, x^73 + 60*x^71 + 76*x^70 + 110*x^69 + 4*x^68 + 12*x^67 + 20*x^66 + 81*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 110*x^5 + 68*x^4 + 76*x^3 + 84*x^2 + 57*x + 92, x^73 + 60*x^71 + 112*x^70 + 6*x^69 + 92*x^67 + 112*x^66 + 105*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 6*x^5 + 28*x^3 + 112*x^2 + 81*x + 32, x^73 + 60*x^71 + 16*x^70 + 54*x^69 + 16*x^68 + 124*x^67 + 48*x^66 + 25*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 54*x^5 + 16*x^4 + 60*x^3 + 48*x^2 + x + 48, x^73 + 60*x^71 + 64*x^70 + 102*x^69 + 16*x^68 + 92*x^67 + 32*x^66 + 9*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 102*x^5 + 16*x^4 + 28*x^3 + 32*x^2 + 113*x + 16, x^73 + 60*x^71 + 36*x^70 + 62*x^69 + 92*x^68 + 108*x^67 + 28*x^66 + 33*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 62*x^5 + 28*x^4 + 44*x^3 + 92*x^2 + 9*x + 36, x^73 + 60*x^71 + 88*x^70 + 118*x^69 + 104*x^68 + 124*x^67 + 104*x^66 + 89*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 118*x^5 + 104*x^4 + 60*x^3 + 104*x^2 + 65*x + 88, x^73 + 60*x^71 + 8*x^70 + 38*x^69 + 40*x^68 + 28*x^67 + 24*x^66 + 9*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 38*x^5 + 40*x^4 + 92*x^3 + 24*x^2 + 113*x + 56, x^73 + 60*x^71 + 120*x^70 + 70*x^69 + 56*x^68 + 28*x^67 + 104*x^66 + 105*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 70*x^5 + 56*x^4 + 92*x^3 + 104*x^2 + 81*x + 104, x^73 + 60*x^71 + 112*x^70 + 6*x^69 + 64*x^68 + 92*x^67 + 112*x^66 + 105*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 6*x^5 + 64*x^4 + 28*x^3 + 112*x^2 + 81*x + 96, x^73 + 60*x^71 + 44*x^70 + 30*x^69 + 116*x^68 + 108*x^67 + 20*x^66 + 65*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 30*x^5 + 52*x^4 + 44*x^3 + 84*x^2 + 41*x + 12, x^73 + 60*x^71 + 72*x^70 + 118*x^69 + 56*x^68 + 124*x^67 + 120*x^66 + 89*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 118*x^5 + 56*x^4 + 60*x^3 + 120*x^2 + 65*x + 8, x^73 + 60*x^71 + 16*x^70 + 38*x^69 + 64*x^68 + 28*x^67 + 16*x^66 + 9*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 38*x^5 + 64*x^4 + 92*x^3 + 16*x^2 + 113*x + 32, x^73 + 60*x^71 + 76*x^70 + 110*x^69 + 100*x^68 + 12*x^67 + 84*x^66 + 81*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 110*x^5 + 36*x^4 + 76*x^3 + 20*x^2 + 57*x + 60, x^73 + 60*x^71 + 36*x^70 + 78*x^69 + 108*x^68 + 12*x^67 + 124*x^66 + 113*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 78*x^5 + 44*x^4 + 76*x^3 + 60*x^2 + 89*x + 52, x^73 + 60*x^71 + 100*x^70 + 62*x^69 + 92*x^68 + 44*x^67 + 28*x^66 + 97*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 62*x^5 + 28*x^4 + 108*x^3 + 92*x^2 + 73*x + 100, x^73 + 60*x^71 + 104*x^70 + 70*x^69 + 8*x^68 + 92*x^67 + 56*x^66 + 41*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 70*x^5 + 8*x^4 + 28*x^3 + 56*x^2 + 17*x + 88, x^73 + 60*x^71 + 12*x^70 + 126*x^69 + 52*x^68 + 108*x^67 + 52*x^66 + 97*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 126*x^5 + 116*x^4 + 44*x^3 + 116*x^2 + 73*x + 76, x^73 + 60*x^71 + 104*x^70 + 22*x^69 + 24*x^68 + 124*x^67 + 24*x^66 + 57*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 22*x^5 + 24*x^4 + 60*x^3 + 24*x^2 + 33*x + 104, x^73 + 60*x^71 + 92*x^70 + 30*x^69 + 36*x^68 + 108*x^67 + 36*x^66 + 65*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 30*x^5 + 100*x^4 + 44*x^3 + 100*x^2 + 41*x + 28, x^73 + 60*x^71 + 112*x^70 + 22*x^69 + 48*x^68 + 124*x^67 + 16*x^66 + 57*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 22*x^5 + 48*x^4 + 60*x^3 + 16*x^2 + 33*x + 80, x^73 + 60*x^71 + 64*x^70 + 38*x^69 + 112*x^68 + 92*x^67 + 96*x^66 + 73*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 38*x^5 + 112*x^4 + 28*x^3 + 96*x^2 + 49*x + 112, x^73 + 60*x^71 + 36*x^70 + 110*x^69 + 44*x^68 + 76*x^67 + 124*x^66 + 17*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 110*x^5 + 108*x^4 + 12*x^3 + 60*x^2 + 121*x + 116, x^73 + 60*x^71 + 72*x^70 + 6*x^69 + 72*x^68 + 92*x^67 + 24*x^66 + 105*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 6*x^5 + 72*x^4 + 28*x^3 + 24*x^2 + 81*x + 88, x^73 + 60*x^71 + 120*x^70 + 54*x^69 + 40*x^68 + 124*x^67 + 8*x^66 + 25*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 54*x^5 + 40*x^4 + 60*x^3 + 8*x^2 + x + 88, x^73 + 60*x^71 + 92*x^70 + 46*x^69 + 116*x^68 + 76*x^67 + 68*x^66 + 81*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 46*x^5 + 52*x^4 + 12*x^3 + 4*x^2 + 57*x + 44, x^73 + 60*x^71 + 116*x^70 + 78*x^69 + 28*x^68 + 76*x^67 + 108*x^66 + 49*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 78*x^5 + 92*x^4 + 12*x^3 + 44*x^2 + 25*x + 68, x^73 + 60*x^71 + 20*x^70 + 62*x^69 + 76*x^68 + 108*x^67 + 108*x^66 + 33*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 62*x^5 + 12*x^4 + 44*x^3 + 44*x^2 + 9*x + 116, x^73 + 60*x^71 + 60*x^70 + 78*x^69 + 116*x^68 + 12*x^67 + 36*x^66 + 113*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 78*x^5 + 52*x^4 + 76*x^3 + 100*x^2 + 89*x + 108, x^73 + 60*x^71 + 40*x^70 + 70*x^69 + 40*x^68 + 92*x^67 + 56*x^66 + 41*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 70*x^5 + 40*x^4 + 28*x^3 + 56*x^2 + 17*x + 120, x^73 + 60*x^71 + 108*x^70 + 30*x^69 + 52*x^68 + 108*x^67 + 84*x^66 + 65*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 30*x^5 + 116*x^4 + 44*x^3 + 20*x^2 + 41*x + 76, x^73 + 60*x^71 + 12*x^70 + 14*x^69 + 68*x^68 + 12*x^67 + 20*x^66 + 49*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 14*x^5 + 4*x^4 + 76*x^3 + 84*x^2 + 25*x + 92, x^73 + 60*x^71 + 20*x^70 + 78*x^69 + 124*x^68 + 12*x^67 + 12*x^66 + 113*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 78*x^5 + 60*x^4 + 76*x^3 + 76*x^2 + 89*x + 36, x^73 + 60*x^71 + 88*x^70 + 118*x^69 + 40*x^68 + 60*x^67 + 40*x^66 + 25*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 118*x^5 + 40*x^4 + 124*x^3 + 40*x^2 + x + 88, x^73 + 60*x^71 + 64*x^70 + 86*x^69 + 32*x^68 + 124*x^67 + 64*x^66 + 121*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 86*x^5 + 32*x^4 + 60*x^3 + 64*x^2 + 97*x + 96, x^73 + 60*x^71 + 60*x^70 + 94*x^69 + 68*x^68 + 44*x^67 + 4*x^66 + 65*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 94*x^5 + 4*x^4 + 108*x^3 + 68*x^2 + 41*x + 60, x^73 + 60*x^71 + 36*x^70 + 14*x^69 + 76*x^68 + 76*x^67 + 124*x^66 + 113*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 14*x^5 + 12*x^4 + 12*x^3 + 60*x^2 + 89*x + 84, x^73 + 60*x^71 + 16*x^70 + 38*x^69 + 92*x^67 + 80*x^66 + 73*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 38*x^5 + 28*x^3 + 80*x^2 + 49*x + 32, x^73 + 60*x^71 + 84*x^70 + 30*x^69 + 12*x^68 + 108*x^67 + 108*x^66 + 65*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 30*x^5 + 76*x^4 + 44*x^3 + 44*x^2 + 41*x + 116, x^73 + 60*x^71 + 44*x^70 + 110*x^69 + 68*x^68 + 76*x^67 + 52*x^66 + 17*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 110*x^5 + 4*x^4 + 12*x^3 + 116*x^2 + 121*x + 28, x^73 + 60*x^71 + 28*x^70 + 14*x^69 + 52*x^68 + 12*x^67 + 4*x^66 + 49*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 14*x^5 + 116*x^4 + 76*x^3 + 68*x^2 + 25*x + 108, x^73 + 60*x^71 + 60*x^70 + 30*x^69 + 4*x^68 + 44*x^67 + 4*x^66 + x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 30*x^5 + 68*x^4 + 108*x^3 + 68*x^2 + 105*x + 124, x^73 + 60*x^71 + 56*x^70 + 86*x^69 + 40*x^68 + 60*x^67 + 72*x^66 + 57*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 86*x^5 + 40*x^4 + 124*x^3 + 72*x^2 + 33*x + 88, x^73 + 60*x^71 + 72*x^70 + 22*x^69 + 88*x^68 + 60*x^67 + 56*x^66 + 121*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 22*x^5 + 88*x^4 + 124*x^3 + 56*x^2 + 97*x + 40, x^73 + 60*x^71 + 16*x^70 + 6*x^69 + 92*x^67 + 16*x^66 + 105*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 6*x^5 + 28*x^3 + 16*x^2 + 81*x + 96, x^73 + 60*x^71 + 108*x^70 + 78*x^69 + 100*x^68 + 12*x^67 + 52*x^66 + 113*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 78*x^5 + 36*x^4 + 76*x^3 + 116*x^2 + 89*x + 60, x^73 + 60*x^71 + 24*x^70 + 54*x^69 + 40*x^68 + 60*x^67 + 104*x^66 + 89*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 54*x^5 + 40*x^4 + 124*x^3 + 104*x^2 + 65*x + 88, x^73 + 60*x^71 + 64*x^70 + 22*x^69 + 64*x^68 + 60*x^67 + 64*x^66 + 121*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 22*x^5 + 64*x^4 + 124*x^3 + 64*x^2 + 97*x + 64, x^73 + 60*x^71 + 52*x^70 + 110*x^69 + 92*x^68 + 76*x^67 + 108*x^66 + 17*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 110*x^5 + 28*x^4 + 12*x^3 + 44*x^2 + 121*x + 68, x^73 + 60*x^71 + 96*x^70 + 38*x^69 + 80*x^68 + 92*x^67 + 64*x^66 + 73*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 38*x^5 + 80*x^4 + 28*x^3 + 64*x^2 + 49*x + 16, x^73 + 60*x^71 + 68*x^70 + 78*x^69 + 44*x^68 + 12*x^67 + 28*x^66 + 113*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 78*x^5 + 108*x^4 + 76*x^3 + 92*x^2 + 89*x + 52, x^73 + 60*x^71 + 124*x^70 + 30*x^69 + 68*x^68 + 44*x^67 + 68*x^66 + x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 30*x^5 + 4*x^4 + 108*x^3 + 4*x^2 + 105*x + 60, x^73 + 60*x^71 + 4*x^70 + 94*x^69 + 28*x^68 + 44*x^67 + 124*x^66 + 65*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 94*x^5 + 92*x^4 + 108*x^3 + 60*x^2 + 41*x + 36, x^73 + 60*x^71 + 92*x^70 + 94*x^69 + 4*x^68 + 108*x^67 + 100*x^66 + x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 94*x^5 + 68*x^4 + 44*x^3 + 36*x^2 + 105*x + 124, x^73 + 60*x^71 + 100*x^70 + 110*x^69 + 108*x^68 + 76*x^67 + 60*x^66 + 17*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 110*x^5 + 44*x^4 + 12*x^3 + 124*x^2 + 121*x + 52, x^73 + 60*x^71 + 92*x^70 + 126*x^69 + 100*x^68 + 44*x^67 + 36*x^66 + 33*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 126*x^5 + 36*x^4 + 108*x^3 + 100*x^2 + 9*x + 92, x^73 + 60*x^71 + 76*x^70 + 62*x^69 + 116*x^68 + 44*x^67 + 52*x^66 + 97*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 62*x^5 + 52*x^4 + 108*x^3 + 116*x^2 + 73*x + 76, x^73 + 60*x^71 + 38*x^69 + 48*x^68 + 28*x^67 + 96*x^66 + 9*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 38*x^5 + 48*x^4 + 92*x^3 + 96*x^2 + 113*x + 112, x^73 + 60*x^71 + 100*x^70 + 78*x^69 + 44*x^68 + 12*x^67 + 60*x^66 + 113*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 78*x^5 + 108*x^4 + 76*x^3 + 124*x^2 + 89*x + 116, x^73 + 60*x^71 + 4*x^70 + 30*x^69 + 60*x^68 + 108*x^67 + 124*x^66 + 65*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 30*x^5 + 124*x^4 + 44*x^3 + 60*x^2 + 41*x + 4, x^73 + 60*x^71 + 28*x^70 + 46*x^69 + 52*x^68 + 12*x^67 + 68*x^66 + 17*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 46*x^5 + 116*x^4 + 76*x^3 + 4*x^2 + 121*x + 44, x^73 + 60*x^71 + 32*x^70 + 102*x^69 + 48*x^68 + 28*x^67 + 73*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 102*x^5 + 48*x^4 + 92*x^3 + 49*x + 48, x^73 + 60*x^71 + 48*x^70 + 22*x^69 + 112*x^68 + 124*x^67 + 80*x^66 + 57*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 22*x^5 + 112*x^4 + 60*x^3 + 80*x^2 + 33*x + 16, x^73 + 60*x^71 + 104*x^70 + 6*x^69 + 40*x^68 + 92*x^67 + 120*x^66 + 105*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 6*x^5 + 40*x^4 + 28*x^3 + 120*x^2 + 81*x + 120, x^73 + 60*x^71 + 40*x^70 + 6*x^69 + 8*x^68 + 92*x^67 + 120*x^66 + 105*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 6*x^5 + 8*x^4 + 28*x^3 + 120*x^2 + 81*x + 88, x^73 + 60*x^71 + 104*x^70 + 102*x^69 + 40*x^68 + 28*x^67 + 120*x^66 + 73*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 102*x^5 + 40*x^4 + 92*x^3 + 120*x^2 + 49*x + 120, x^73 + 60*x^71 + 28*x^70 + 14*x^69 + 52*x^68 + 76*x^67 + 68*x^66 + 113*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 14*x^5 + 116*x^4 + 12*x^3 + 4*x^2 + 89*x + 44, x^73 + 60*x^71 + 52*x^70 + 30*x^69 + 44*x^68 + 44*x^67 + 76*x^66 + x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 30*x^5 + 108*x^4 + 108*x^3 + 12*x^2 + 105*x + 20, x^73 + 60*x^71 + 28*x^70 + 126*x^69 + 100*x^68 + 108*x^67 + 36*x^66 + 97*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 126*x^5 + 36*x^4 + 44*x^3 + 100*x^2 + 73*x + 28, x^73 + 60*x^71 + 52*x^70 + 62*x^69 + 44*x^68 + 44*x^67 + 12*x^66 + 97*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 62*x^5 + 108*x^4 + 108*x^3 + 76*x^2 + 73*x + 84, x^73 + 60*x^71 + 8*x^70 + 70*x^69 + 8*x^68 + 92*x^67 + 88*x^66 + 41*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 70*x^5 + 8*x^4 + 28*x^3 + 88*x^2 + 17*x + 24, x^73 + 60*x^71 + 16*x^70 + 22*x^69 + 112*x^68 + 124*x^67 + 48*x^66 + 57*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 22*x^5 + 112*x^4 + 60*x^3 + 48*x^2 + 33*x + 80, x^73 + 60*x^71 + 96*x^70 + 86*x^69 + 32*x^68 + 124*x^67 + 96*x^66 + 121*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 86*x^5 + 32*x^4 + 60*x^3 + 96*x^2 + 97*x + 32, x^73 + 60*x^71 + 84*x^70 + 126*x^69 + 44*x^68 + 44*x^67 + 44*x^66 + 33*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 126*x^5 + 108*x^4 + 108*x^3 + 108*x^2 + 9*x + 20, x^73 + 60*x^71 + 112*x^70 + 54*x^69 + 80*x^68 + 60*x^67 + 80*x^66 + 89*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 54*x^5 + 80*x^4 + 124*x^3 + 80*x^2 + 65*x + 112, x^73 + 60*x^71 + 40*x^70 + 6*x^69 + 104*x^68 + 28*x^67 + 120*x^66 + 41*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 6*x^5 + 104*x^4 + 92*x^3 + 120*x^2 + 17*x + 120, x^73 + 60*x^71 + 56*x^70 + 118*x^69 + 72*x^68 + 124*x^67 + 8*x^66 + 89*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 118*x^5 + 72*x^4 + 60*x^3 + 8*x^2 + 65*x + 120, x^73 + 60*x^71 + 36*x^70 + 14*x^69 + 12*x^68 + 12*x^67 + 60*x^66 + 49*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 14*x^5 + 76*x^4 + 76*x^3 + 124*x^2 + 25*x + 84, x^73 + 60*x^71 + 60*x^70 + 94*x^69 + 100*x^68 + 44*x^67 + 68*x^66 + 65*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 94*x^5 + 36*x^4 + 108*x^3 + 4*x^2 + 41*x + 92, x^73 + 60*x^71 + 76*x^70 + 62*x^69 + 52*x^68 + 44*x^67 + 52*x^66 + 97*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 62*x^5 + 116*x^4 + 108*x^3 + 116*x^2 + 73*x + 12, x^73 + 60*x^71 + 104*x^70 + 118*x^69 + 56*x^68 + 124*x^67 + 24*x^66 + 89*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 118*x^5 + 56*x^4 + 60*x^3 + 24*x^2 + 65*x + 72, x^73 + 60*x^71 + 16*x^70 + 38*x^69 + 64*x^68 + 92*x^67 + 80*x^66 + 73*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 38*x^5 + 64*x^4 + 28*x^3 + 80*x^2 + 49*x + 96, x^73 + 60*x^71 + 84*x^70 + 62*x^69 + 76*x^68 + 108*x^67 + 44*x^66 + 33*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 62*x^5 + 12*x^4 + 44*x^3 + 108*x^2 + 9*x + 116, x^73 + 60*x^71 + 38*x^69 + 112*x^68 + 28*x^67 + 96*x^66 + 9*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 38*x^5 + 112*x^4 + 92*x^3 + 96*x^2 + 113*x + 48, x^73 + 60*x^71 + 104*x^70 + 86*x^69 + 56*x^68 + 124*x^67 + 88*x^66 + 121*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 86*x^5 + 56*x^4 + 60*x^3 + 88*x^2 + 97*x + 8, x^73 + 60*x^71 + 36*x^70 + 110*x^69 + 12*x^68 + 12*x^67 + 124*x^66 + 81*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 110*x^5 + 76*x^4 + 76*x^3 + 60*x^2 + 57*x + 20, x^73 + 60*x^71 + 104*x^70 + 70*x^69 + 72*x^68 + 92*x^67 + 56*x^66 + 41*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 70*x^5 + 72*x^4 + 28*x^3 + 56*x^2 + 17*x + 24, x^73 + 60*x^71 + 28*x^70 + 62*x^69 + 4*x^68 + 44*x^67 + 36*x^66 + 97*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 62*x^5 + 68*x^4 + 108*x^3 + 100*x^2 + 73*x + 124, x^73 + 60*x^71 + 112*x^70 + 102*x^69 + 32*x^68 + 28*x^67 + 48*x^66 + 73*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 102*x^5 + 32*x^4 + 92*x^3 + 48*x^2 + 49*x + 64, x^73 + 60*x^71 + 72*x^70 + 38*x^69 + 8*x^68 + 28*x^67 + 24*x^66 + 9*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 38*x^5 + 8*x^4 + 92*x^3 + 24*x^2 + 113*x + 24, x^73 + 60*x^71 + 108*x^70 + 78*x^69 + 4*x^68 + 76*x^67 + 52*x^66 + 49*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 78*x^5 + 68*x^4 + 12*x^3 + 116*x^2 + 25*x + 28, x^73 + 60*x^71 + 96*x^70 + 54*x^69 + 96*x^68 + 60*x^67 + 96*x^66 + 89*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 54*x^5 + 96*x^4 + 124*x^3 + 96*x^2 + 65*x + 96, x^73 + 60*x^71 + 28*x^70 + 78*x^69 + 116*x^68 + 76*x^67 + 68*x^66 + 49*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 78*x^5 + 52*x^4 + 12*x^3 + 4*x^2 + 25*x + 108, x^73 + 60*x^71 + 80*x^70 + 38*x^69 + 32*x^68 + 92*x^67 + 80*x^66 + 73*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 38*x^5 + 32*x^4 + 28*x^3 + 80*x^2 + 49*x + 64, x^73 + 60*x^71 + 64*x^70 + 54*x^69 + 96*x^68 + 60*x^67 + 64*x^66 + 89*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 54*x^5 + 96*x^4 + 124*x^3 + 64*x^2 + 65*x + 32, x^73 + 60*x^71 + 52*x^70 + 78*x^69 + 28*x^68 + 76*x^67 + 44*x^66 + 49*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 78*x^5 + 92*x^4 + 12*x^3 + 108*x^2 + 25*x + 68, x^73 + 60*x^71 + 4*x^70 + 14*x^69 + 76*x^68 + 12*x^67 + 28*x^66 + 49*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 14*x^5 + 12*x^4 + 76*x^3 + 92*x^2 + 25*x + 84, x^73 + 60*x^71 + 80*x^70 + 102*x^69 + 96*x^68 + 92*x^67 + 80*x^66 + 9*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 102*x^5 + 96*x^4 + 28*x^3 + 80*x^2 + 113*x, x^73 + 60*x^71 + 124*x^70 + 94*x^69 + 68*x^68 + 108*x^67 + 4*x^66 + x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 94*x^5 + 4*x^4 + 44*x^3 + 68*x^2 + 105*x + 124, x^73 + 60*x^71 + 120*x^70 + 86*x^69 + 40*x^68 + 124*x^67 + 72*x^66 + 121*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 86*x^5 + 40*x^4 + 60*x^3 + 72*x^2 + 97*x + 24, x^73 + 60*x^71 + 44*x^70 + 78*x^69 + 100*x^68 + 12*x^67 + 116*x^66 + 113*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 78*x^5 + 36*x^4 + 76*x^3 + 52*x^2 + 89*x + 60, x^73 + 60*x^71 + 52*x^70 + 62*x^69 + 44*x^68 + 108*x^67 + 76*x^66 + 33*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 62*x^5 + 108*x^4 + 44*x^3 + 12*x^2 + 9*x + 20, x^73 + 60*x^71 + 64*x^70 + 102*x^69 + 80*x^68 + 92*x^67 + 32*x^66 + 9*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 102*x^5 + 80*x^4 + 28*x^3 + 32*x^2 + 113*x + 80, x^73 + 60*x^71 + 4*x^70 + 110*x^69 + 76*x^68 + 76*x^67 + 28*x^66 + 17*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 110*x^5 + 12*x^4 + 12*x^3 + 92*x^2 + 121*x + 84, x^73 + 60*x^71 + 32*x^70 + 102*x^69 + 80*x^68 + 28*x^67 + 64*x^66 + 73*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 102*x^5 + 80*x^4 + 92*x^3 + 64*x^2 + 49*x + 80, x^73 + 60*x^71 + 112*x^70 + 118*x^69 + 48*x^68 + 60*x^67 + 16*x^66 + 25*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 118*x^5 + 48*x^4 + 124*x^3 + 16*x^2 + x + 80, x^73 + 60*x^71 + 100*x^70 + 94*x^69 + 92*x^68 + 44*x^67 + 92*x^66 + 65*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 94*x^5 + 28*x^4 + 108*x^3 + 28*x^2 + 41*x + 36, x^73 + 60*x^71 + 60*x^70 + 110*x^69 + 84*x^68 + 12*x^67 + 36*x^66 + 81*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 110*x^5 + 20*x^4 + 76*x^3 + 100*x^2 + 57*x + 12, x^73 + 60*x^71 + 68*x^70 + 14*x^69 + 44*x^68 + 76*x^67 + 92*x^66 + 113*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 14*x^5 + 108*x^4 + 12*x^3 + 28*x^2 + 89*x + 116, x^73 + 60*x^71 + 80*x^70 + 86*x^69 + 48*x^68 + 124*x^67 + 112*x^66 + 121*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 86*x^5 + 48*x^4 + 60*x^3 + 112*x^2 + 97*x + 16, x^73 + 60*x^71 + 124*x^70 + 14*x^69 + 84*x^68 + 12*x^67 + 36*x^66 + 49*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 14*x^5 + 20*x^4 + 76*x^3 + 100*x^2 + 25*x + 76, x^73 + 60*x^71 + 4*x^70 + 126*x^69 + 124*x^68 + 108*x^67 + 60*x^66 + 97*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 126*x^5 + 60*x^4 + 44*x^3 + 124*x^2 + 73*x + 4, x^73 + 60*x^71 + 100*x^70 + 14*x^69 + 12*x^68 + 12*x^67 + 124*x^66 + 49*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 14*x^5 + 76*x^4 + 76*x^3 + 60*x^2 + 25*x + 84, x^73 + 60*x^71 + 4*x^70 + 78*x^69 + 44*x^68 + 76*x^67 + 28*x^66 + 49*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 78*x^5 + 108*x^4 + 12*x^3 + 92*x^2 + 25*x + 116, x^73 + 60*x^71 + 76*x^70 + 14*x^69 + 100*x^68 + 76*x^67 + 84*x^66 + 113*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 14*x^5 + 36*x^4 + 12*x^3 + 20*x^2 + 89*x + 60, x^73 + 60*x^71 + 124*x^70 + 78*x^69 + 116*x^68 + 12*x^67 + 100*x^66 + 113*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 78*x^5 + 52*x^4 + 76*x^3 + 36*x^2 + 89*x + 108, x^73 + 60*x^71 + 96*x^70 + 38*x^69 + 48*x^68 + 92*x^67 + 73*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 38*x^5 + 48*x^4 + 28*x^3 + 49*x + 112, x^73 + 60*x^71 + 118*x^69 + 32*x^68 + 60*x^67 + 25*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 118*x^5 + 32*x^4 + 124*x^3 + x + 96, x^73 + 60*x^71 + 48*x^70 + 54*x^69 + 48*x^68 + 124*x^67 + 16*x^66 + 25*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 54*x^5 + 48*x^4 + 60*x^3 + 16*x^2 + x + 16, x^73 + 60*x^71 + 92*x^70 + 46*x^69 + 52*x^68 + 76*x^67 + 68*x^66 + 81*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 46*x^5 + 116*x^4 + 12*x^3 + 4*x^2 + 57*x + 108, x^73 + 60*x^71 + 48*x^70 + 22*x^69 + 80*x^68 + 60*x^67 + 80*x^66 + 121*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 22*x^5 + 80*x^4 + 124*x^3 + 80*x^2 + 97*x + 48, x^73 + 60*x^71 + 116*x^70 + 126*x^69 + 44*x^68 + 44*x^67 + 76*x^66 + 33*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 126*x^5 + 108*x^4 + 108*x^3 + 12*x^2 + 9*x + 84, x^73 + 60*x^71 + 72*x^70 + 38*x^69 + 104*x^68 + 92*x^67 + 24*x^66 + 73*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 38*x^5 + 104*x^4 + 28*x^3 + 24*x^2 + 49*x + 56, x^73 + 60*x^71 + 68*x^70 + 94*x^69 + 60*x^68 + 108*x^67 + 60*x^66 + x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 94*x^5 + 124*x^4 + 44*x^3 + 124*x^2 + 105*x + 4, x^73 + 60*x^71 + 28*x^70 + 46*x^69 + 20*x^68 + 12*x^67 + 4*x^66 + 17*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 46*x^5 + 84*x^4 + 76*x^3 + 68*x^2 + 121*x + 12, x^73 + 60*x^71 + 28*x^70 + 126*x^69 + 68*x^68 + 44*x^67 + 36*x^66 + 33*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 126*x^5 + 4*x^4 + 108*x^3 + 100*x^2 + 9*x + 60, x^73 + 60*x^71 + 116*x^70 + 126*x^69 + 44*x^68 + 108*x^67 + 12*x^66 + 97*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 126*x^5 + 108*x^4 + 44*x^3 + 76*x^2 + 73*x + 20, x^73 + 60*x^71 + 80*x^70 + 86*x^69 + 16*x^68 + 60*x^67 + 112*x^66 + 57*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 86*x^5 + 16*x^4 + 124*x^3 + 112*x^2 + 33*x + 48, x^73 + 60*x^71 + 76*x^70 + 14*x^69 + 68*x^68 + 12*x^67 + 84*x^66 + 49*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 14*x^5 + 4*x^4 + 76*x^3 + 20*x^2 + 25*x + 92, x^73 + 60*x^71 + 4*x^70 + 94*x^69 + 60*x^68 + 108*x^67 + 124*x^66 + x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 94*x^5 + 124*x^4 + 44*x^3 + 60*x^2 + 105*x + 4, x^73 + 60*x^71 + 112*x^70 + 70*x^69 + 28*x^67 + 48*x^66 + 105*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 70*x^5 + 92*x^3 + 48*x^2 + 81*x + 96, x^73 + 60*x^71 + 48*x^70 + 54*x^69 + 80*x^68 + 124*x^67 + 80*x^66 + 25*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 54*x^5 + 80*x^4 + 60*x^3 + 80*x^2 + x + 48, x^73 + 60*x^71 + 44*x^70 + 14*x^69 + 4*x^68 + 76*x^67 + 116*x^66 + 113*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 14*x^5 + 68*x^4 + 12*x^3 + 52*x^2 + 89*x + 28, x^73 + 60*x^71 + 68*x^70 + 62*x^69 + 28*x^68 + 44*x^67 + 124*x^66 + 97*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 62*x^5 + 92*x^4 + 108*x^3 + 60*x^2 + 73*x + 100, x^73 + 60*x^71 + 8*x^70 + 118*x^69 + 56*x^68 + 124*x^67 + 56*x^66 + 89*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 118*x^5 + 56*x^4 + 60*x^3 + 56*x^2 + 65*x + 8, x^73 + 60*x^71 + 8*x^70 + 6*x^69 + 104*x^68 + 92*x^67 + 24*x^66 + 105*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 6*x^5 + 104*x^4 + 28*x^3 + 24*x^2 + 81*x + 120, x^73 + 60*x^71 + 44*x^70 + 62*x^69 + 20*x^68 + 108*x^67 + 20*x^66 + 33*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 62*x^5 + 84*x^4 + 44*x^3 + 84*x^2 + 9*x + 108, x^73 + 60*x^71 + 120*x^70 + 86*x^69 + 8*x^68 + 124*x^67 + 8*x^66 + 121*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 86*x^5 + 8*x^4 + 60*x^3 + 8*x^2 + 97*x + 120, x^73 + 60*x^71 + 36*x^70 + 110*x^69 + 76*x^68 + 76*x^67 + 60*x^66 + 17*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 110*x^5 + 12*x^4 + 12*x^3 + 124*x^2 + 121*x + 20, x^73 + 60*x^71 + 48*x^70 + 38*x^69 + 64*x^68 + 92*x^67 + 112*x^66 + 73*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 38*x^5 + 64*x^4 + 28*x^3 + 112*x^2 + 49*x + 32, x^73 + 60*x^71 + 24*x^70 + 118*x^69 + 72*x^68 + 124*x^67 + 104*x^66 + 89*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 118*x^5 + 72*x^4 + 60*x^3 + 104*x^2 + 65*x + 56, x^73 + 60*x^71 + 32*x^70 + 86*x^69 + 64*x^68 + 124*x^67 + 96*x^66 + 121*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 86*x^5 + 64*x^4 + 60*x^3 + 96*x^2 + 97*x + 64, x^73 + 60*x^71 + 68*x^70 + 110*x^69 + 76*x^68 + 76*x^67 + 92*x^66 + 17*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 110*x^5 + 12*x^4 + 12*x^3 + 28*x^2 + 121*x + 84, x^73 + 60*x^71 + 116*x^70 + 94*x^69 + 12*x^68 + 108*x^67 + 12*x^66 + x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 94*x^5 + 76*x^4 + 44*x^3 + 76*x^2 + 105*x + 52, x^73 + 60*x^71 + 12*x^70 + 62*x^69 + 52*x^68 + 108*x^67 + 52*x^66 + 33*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 62*x^5 + 116*x^4 + 44*x^3 + 116*x^2 + 9*x + 76, x^73 + 60*x^71 + 96*x^70 + 38*x^69 + 112*x^68 + 92*x^67 + 73*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 38*x^5 + 112*x^4 + 28*x^3 + 49*x + 48, x^73 + 60*x^71 + 48*x^70 + 102*x^69 + 96*x^68 + 28*x^67 + 112*x^66 + 73*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 102*x^5 + 96*x^4 + 92*x^3 + 112*x^2 + 49*x, x^73 + 60*x^71 + 92*x^70 + 126*x^69 + 68*x^68 + 108*x^67 + 36*x^66 + 97*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 126*x^5 + 4*x^4 + 44*x^3 + 100*x^2 + 73*x + 124, x^73 + 60*x^71 + 12*x^70 + 14*x^69 + 4*x^68 + 12*x^67 + 20*x^66 + 49*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 14*x^5 + 68*x^4 + 76*x^3 + 84*x^2 + 25*x + 28, x^73 + 60*x^71 + 36*x^70 + 110*x^69 + 108*x^68 + 12*x^67 + 60*x^66 + 81*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 110*x^5 + 44*x^4 + 76*x^3 + 124*x^2 + 57*x + 116, x^73 + 60*x^71 + 68*x^70 + 110*x^69 + 12*x^68 + 76*x^67 + 92*x^66 + 17*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 110*x^5 + 76*x^4 + 12*x^3 + 28*x^2 + 121*x + 20, x^73 + 60*x^71 + 100*x^70 + 46*x^69 + 12*x^68 + 12*x^67 + 60*x^66 + 17*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 46*x^5 + 76*x^4 + 76*x^3 + 124*x^2 + 121*x + 20, x^73 + 60*x^71 + 40*x^70 + 70*x^69 + 72*x^68 + 28*x^67 + 56*x^66 + 105*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 70*x^5 + 72*x^4 + 92*x^3 + 56*x^2 + 81*x + 88, x^73 + 60*x^71 + 84*x^70 + 62*x^69 + 76*x^68 + 44*x^67 + 108*x^66 + 97*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 62*x^5 + 12*x^4 + 108*x^3 + 44*x^2 + 73*x + 52, x^73 + 60*x^71 + 40*x^70 + 22*x^69 + 88*x^68 + 124*x^67 + 88*x^66 + 57*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 22*x^5 + 88*x^4 + 60*x^3 + 88*x^2 + 33*x + 40, x^73 + 60*x^71 + 100*x^70 + 30*x^69 + 60*x^68 + 44*x^67 + 28*x^66 + x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 30*x^5 + 124*x^4 + 108*x^3 + 92*x^2 + 105*x + 4, x^73 + 60*x^71 + 108*x^70 + 30*x^69 + 84*x^68 + 44*x^67 + 84*x^66 + x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 30*x^5 + 20*x^4 + 108*x^3 + 20*x^2 + 105*x + 44, x^73 + 60*x^71 + 112*x^70 + 70*x^69 + 96*x^68 + 28*x^67 + 112*x^66 + 105*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 70*x^5 + 96*x^4 + 92*x^3 + 112*x^2 + 81*x + 64, x^73 + 60*x^71 + 124*x^70 + 94*x^69 + 68*x^68 + 44*x^67 + 68*x^66 + 65*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 94*x^5 + 4*x^4 + 108*x^3 + 4*x^2 + 41*x + 60, x^73 + 60*x^71 + 48*x^70 + 86*x^69 + 48*x^68 + 60*x^67 + 16*x^66 + 57*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 86*x^5 + 48*x^4 + 124*x^3 + 16*x^2 + 33*x + 16, x^73 + 60*x^71 + 4*x^70 + 78*x^69 + 12*x^68 + 76*x^67 + 92*x^66 + 49*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 78*x^5 + 76*x^4 + 12*x^3 + 28*x^2 + 25*x + 84, x^73 + 60*x^71 + 88*x^70 + 102*x^69 + 120*x^68 + 92*x^67 + 72*x^66 + 9*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 102*x^5 + 120*x^4 + 28*x^3 + 72*x^2 + 113*x + 104, x^73 + 60*x^71 + 48*x^70 + 102*x^69 + 92*x^67 + 112*x^66 + 9*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 102*x^5 + 28*x^3 + 112*x^2 + 113*x + 96, x^73 + 60*x^71 + 104*x^70 + 38*x^69 + 72*x^68 + 28*x^67 + 56*x^66 + 9*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 38*x^5 + 72*x^4 + 92*x^3 + 56*x^2 + 113*x + 24, x^73 + 60*x^71 + 96*x^70 + 22*x^69 + 124*x^67 + 32*x^66 + 57*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 22*x^5 + 60*x^3 + 32*x^2 + 33*x, x^73 + 60*x^71 + 32*x^70 + 54*x^69 + 32*x^68 + 60*x^67 + 32*x^66 + 89*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 54*x^5 + 32*x^4 + 124*x^3 + 32*x^2 + 65*x + 32, x^73 + 60*x^71 + 8*x^70 + 86*x^69 + 24*x^68 + 60*x^67 + 120*x^66 + 57*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 86*x^5 + 24*x^4 + 124*x^3 + 120*x^2 + 33*x + 104, x^73 + 60*x^71 + 80*x^70 + 6*x^69 + 92*x^67 + 80*x^66 + 105*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 6*x^5 + 28*x^3 + 80*x^2 + 81*x + 96, x^73 + 60*x^71 + 48*x^70 + 54*x^69 + 16*x^68 + 124*x^67 + 80*x^66 + 25*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 54*x^5 + 16*x^4 + 60*x^3 + 80*x^2 + x + 112, x^73 + 60*x^71 + 52*x^70 + 110*x^69 + 28*x^68 + 12*x^67 + 44*x^66 + 81*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 110*x^5 + 92*x^4 + 76*x^3 + 108*x^2 + 57*x + 68, x^73 + 60*x^71 + 40*x^70 + 118*x^69 + 88*x^68 + 60*x^67 + 88*x^66 + 25*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 118*x^5 + 88*x^4 + 124*x^3 + 88*x^2 + x + 40, x^73 + 60*x^71 + 4*x^70 + 110*x^69 + 44*x^68 + 76*x^67 + 92*x^66 + 17*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 110*x^5 + 108*x^4 + 12*x^3 + 28*x^2 + 121*x + 52, x^73 + 60*x^71 + 32*x^70 + 54*x^69 + 96*x^68 + 60*x^67 + 32*x^66 + 89*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 54*x^5 + 96*x^4 + 124*x^3 + 32*x^2 + 65*x + 96, x^73 + 60*x^71 + 24*x^70 + 118*x^69 + 8*x^68 + 60*x^67 + 40*x^66 + 25*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 118*x^5 + 8*x^4 + 124*x^3 + 40*x^2 + x + 56, x^73 + 60*x^71 + 116*x^70 + 78*x^69 + 28*x^68 + 12*x^67 + 44*x^66 + 113*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 78*x^5 + 92*x^4 + 76*x^3 + 108*x^2 + 89*x + 4, x^73 + 60*x^71 + 48*x^70 + 22*x^69 + 16*x^68 + 124*x^67 + 16*x^66 + 57*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 22*x^5 + 16*x^4 + 60*x^3 + 16*x^2 + 33*x + 48, x^73 + 60*x^71 + 72*x^70 + 86*x^69 + 56*x^68 + 124*x^67 + 56*x^66 + 121*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 86*x^5 + 56*x^4 + 60*x^3 + 56*x^2 + 97*x + 72, x^73 + 60*x^71 + 48*x^70 + 38*x^69 + 64*x^68 + 28*x^67 + 48*x^66 + 9*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 38*x^5 + 64*x^4 + 92*x^3 + 48*x^2 + 113*x + 96, x^73 + 60*x^71 + 76*x^70 + 94*x^69 + 20*x^68 + 44*x^67 + 52*x^66 + 65*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 94*x^5 + 84*x^4 + 108*x^3 + 116*x^2 + 41*x + 44, x^73 + 60*x^71 + 60*x^70 + 14*x^69 + 84*x^68 + 12*x^67 + 100*x^66 + 49*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 14*x^5 + 20*x^4 + 76*x^3 + 36*x^2 + 25*x + 76, x^73 + 60*x^71 + 104*x^70 + 54*x^69 + 88*x^68 + 60*x^67 + 24*x^66 + 89*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 54*x^5 + 88*x^4 + 124*x^3 + 24*x^2 + 65*x + 40, x^73 + 60*x^71 + 120*x^70 + 118*x^69 + 104*x^68 + 124*x^67 + 8*x^66 + 89*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 118*x^5 + 104*x^4 + 60*x^3 + 8*x^2 + 65*x + 24, x^73 + 60*x^71 + 56*x^70 + 6*x^69 + 24*x^68 + 92*x^67 + 40*x^66 + 105*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 6*x^5 + 24*x^4 + 28*x^3 + 40*x^2 + 81*x + 8, x^73 + 60*x^71 + 116*x^70 + 62*x^69 + 44*x^68 + 108*x^67 + 12*x^66 + 33*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 62*x^5 + 108*x^4 + 44*x^3 + 76*x^2 + 9*x + 20, x^73 + 60*x^71 + 28*x^70 + 78*x^69 + 52*x^68 + 12*x^67 + 4*x^66 + 113*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 78*x^5 + 116*x^4 + 76*x^3 + 68*x^2 + 89*x + 108, x^73 + 60*x^71 + 116*x^70 + 30*x^69 + 12*x^68 + 108*x^67 + 12*x^66 + 65*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 30*x^5 + 76*x^4 + 44*x^3 + 76*x^2 + 41*x + 52, x^73 + 60*x^71 + 116*x^70 + 110*x^69 + 124*x^68 + 76*x^67 + 108*x^66 + 17*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 110*x^5 + 60*x^4 + 12*x^3 + 44*x^2 + 121*x + 100, x^73 + 60*x^71 + 48*x^70 + 118*x^69 + 16*x^68 + 60*x^67 + 16*x^66 + 25*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 118*x^5 + 16*x^4 + 124*x^3 + 16*x^2 + x + 48, x^73 + 60*x^71 + 54*x^69 + 96*x^68 + 124*x^67 + 64*x^66 + 25*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 54*x^5 + 96*x^4 + 60*x^3 + 64*x^2 + x + 96, x^73 + 60*x^71 + 20*x^70 + 14*x^69 + 60*x^68 + 12*x^67 + 12*x^66 + 49*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 14*x^5 + 124*x^4 + 76*x^3 + 76*x^2 + 25*x + 100, x^73 + 60*x^71 + 76*x^70 + 62*x^69 + 20*x^68 + 108*x^67 + 52*x^66 + 33*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 62*x^5 + 84*x^4 + 44*x^3 + 116*x^2 + 9*x + 44, x^73 + 60*x^71 + 20*x^70 + 62*x^69 + 108*x^68 + 44*x^67 + 108*x^66 + 97*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 62*x^5 + 44*x^4 + 108*x^3 + 44*x^2 + 73*x + 84, x^73 + 60*x^71 + 60*x^70 + 46*x^69 + 84*x^68 + 12*x^67 + 36*x^66 + 17*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 46*x^5 + 20*x^4 + 76*x^3 + 100*x^2 + 121*x + 12, x^73 + 60*x^71 + 56*x^70 + 38*x^69 + 88*x^68 + 28*x^67 + 40*x^66 + 9*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 38*x^5 + 88*x^4 + 92*x^3 + 40*x^2 + 113*x + 72, x^73 + 60*x^71 + 38*x^69 + 16*x^68 + 92*x^67 + 96*x^66 + 73*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 38*x^5 + 16*x^4 + 28*x^3 + 96*x^2 + 49*x + 16, x^73 + 60*x^71 + 56*x^70 + 6*x^69 + 120*x^68 + 28*x^67 + 40*x^66 + 41*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 6*x^5 + 120*x^4 + 92*x^3 + 40*x^2 + 17*x + 40, x^73 + 60*x^71 + 48*x^70 + 6*x^69 + 32*x^68 + 28*x^67 + 48*x^66 + 41*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 6*x^5 + 32*x^4 + 92*x^3 + 48*x^2 + 17*x, x^73 + 60*x^71 + 120*x^70 + 54*x^69 + 72*x^68 + 124*x^67 + 72*x^66 + 25*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 54*x^5 + 72*x^4 + 60*x^3 + 72*x^2 + x + 120, x^73 + 60*x^71 + 124*x^70 + 126*x^69 + 36*x^68 + 44*x^67 + 68*x^66 + 33*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 126*x^5 + 100*x^4 + 108*x^3 + 4*x^2 + 9*x + 92, x^73 + 60*x^71 + 92*x^70 + 30*x^69 + 68*x^68 + 44*x^67 + 36*x^66 + x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 30*x^5 + 4*x^4 + 108*x^3 + 100*x^2 + 105*x + 124, x^73 + 60*x^71 + 48*x^70 + 22*x^69 + 16*x^68 + 60*x^67 + 80*x^66 + 121*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 22*x^5 + 16*x^4 + 124*x^3 + 80*x^2 + 97*x + 112, x^73 + 60*x^71 + 116*x^70 + 46*x^69 + 124*x^68 + 12*x^67 + 44*x^66 + 17*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 46*x^5 + 60*x^4 + 76*x^3 + 108*x^2 + 121*x + 36, x^73 + 60*x^71 + 100*x^70 + 94*x^69 + 60*x^68 + 44*x^67 + 28*x^66 + 65*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 94*x^5 + 124*x^4 + 108*x^3 + 92*x^2 + 41*x + 4, x^73 + 60*x^71 + 104*x^70 + 54*x^69 + 24*x^68 + 60*x^67 + 24*x^66 + 89*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 54*x^5 + 24*x^4 + 124*x^3 + 24*x^2 + 65*x + 104, x^73 + 60*x^71 + 124*x^70 + 14*x^69 + 20*x^68 + 12*x^67 + 36*x^66 + 49*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 14*x^5 + 84*x^4 + 76*x^3 + 100*x^2 + 25*x + 12, x^73 + 60*x^71 + 8*x^70 + 38*x^69 + 72*x^68 + 92*x^67 + 24*x^66 + 73*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 38*x^5 + 72*x^4 + 28*x^3 + 24*x^2 + 49*x + 24, x^73 + 60*x^71 + 12*x^70 + 46*x^69 + 100*x^68 + 12*x^67 + 20*x^66 + 17*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 46*x^5 + 36*x^4 + 76*x^3 + 84*x^2 + 121*x + 60, x^73 + 60*x^71 + 24*x^70 + 102*x^69 + 88*x^68 + 92*x^67 + 72*x^66 + 9*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 102*x^5 + 88*x^4 + 28*x^3 + 72*x^2 + 113*x + 72, x^73 + 60*x^71 + 36*x^70 + 110*x^69 + 44*x^68 + 12*x^67 + 60*x^66 + 81*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 110*x^5 + 108*x^4 + 76*x^3 + 124*x^2 + 57*x + 52, x^73 + 60*x^71 + 24*x^70 + 70*x^69 + 88*x^68 + 92*x^67 + 8*x^66 + 41*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 70*x^5 + 88*x^4 + 28*x^3 + 8*x^2 + 17*x + 8, x^73 + 60*x^71 + 12*x^70 + 62*x^69 + 116*x^68 + 44*x^67 + 116*x^66 + 97*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 62*x^5 + 52*x^4 + 108*x^3 + 52*x^2 + 73*x + 76, x^73 + 60*x^71 + 80*x^70 + 54*x^69 + 48*x^68 + 124*x^67 + 48*x^66 + 25*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 54*x^5 + 48*x^4 + 60*x^3 + 48*x^2 + x + 80, x^73 + 60*x^71 + 104*x^70 + 6*x^69 + 72*x^68 + 28*x^67 + 120*x^66 + 41*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 6*x^5 + 72*x^4 + 92*x^3 + 120*x^2 + 17*x + 88, x^73 + 60*x^71 + 92*x^70 + 62*x^69 + 4*x^68 + 44*x^67 + 100*x^66 + 97*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 62*x^5 + 68*x^4 + 108*x^3 + 36*x^2 + 73*x + 124, x^73 + 60*x^71 + 36*x^70 + 30*x^69 + 60*x^68 + 44*x^67 + 92*x^66 + x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 30*x^5 + 124*x^4 + 108*x^3 + 28*x^2 + 105*x + 4, x^73 + 60*x^71 + 120*x^70 + 6*x^69 + 120*x^68 + 92*x^67 + 40*x^66 + 105*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 6*x^5 + 120*x^4 + 28*x^3 + 40*x^2 + 81*x + 104, x^73 + 60*x^71 + 22*x^69 + 96*x^68 + 60*x^67 + 64*x^66 + 121*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 22*x^5 + 96*x^4 + 124*x^3 + 64*x^2 + 97*x + 96, x^73 + 60*x^71 + 120*x^70 + 22*x^69 + 104*x^68 + 60*x^67 + 8*x^66 + 121*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 22*x^5 + 104*x^4 + 124*x^3 + 8*x^2 + 97*x + 24, x^73 + 60*x^71 + 52*x^70 + 30*x^69 + 76*x^68 + 108*x^67 + 76*x^66 + 65*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 30*x^5 + 12*x^4 + 44*x^3 + 12*x^2 + 41*x + 116, x^73 + 60*x^71 + 24*x^70 + 6*x^69 + 24*x^68 + 92*x^67 + 8*x^66 + 105*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 6*x^5 + 24*x^4 + 28*x^3 + 8*x^2 + 81*x + 72, x^73 + 60*x^71 + 44*x^70 + 30*x^69 + 84*x^68 + 44*x^67 + 20*x^66 + x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 30*x^5 + 20*x^4 + 108*x^3 + 84*x^2 + 105*x + 44, x^73 + 60*x^71 + 12*x^70 + 126*x^69 + 116*x^68 + 44*x^67 + 116*x^66 + 33*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 126*x^5 + 52*x^4 + 108*x^3 + 52*x^2 + 9*x + 76, x^73 + 60*x^71 + 44*x^70 + 46*x^69 + 4*x^68 + 12*x^67 + 116*x^66 + 17*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 46*x^5 + 68*x^4 + 76*x^3 + 52*x^2 + 121*x + 28, x^73 + 60*x^71 + 56*x^70 + 38*x^69 + 56*x^68 + 92*x^67 + 40*x^66 + 73*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 38*x^5 + 56*x^4 + 28*x^3 + 40*x^2 + 49*x + 104, x^73 + 60*x^71 + 92*x^70 + 126*x^69 + 68*x^68 + 44*x^67 + 100*x^66 + 33*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 126*x^5 + 4*x^4 + 108*x^3 + 36*x^2 + 9*x + 60, x^73 + 60*x^71 + 96*x^70 + 38*x^69 + 80*x^68 + 28*x^67 + 9*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 38*x^5 + 80*x^4 + 92*x^3 + 113*x + 80, x^73 + 60*x^71 + 48*x^70 + 54*x^69 + 48*x^68 + 60*x^67 + 80*x^66 + 89*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 54*x^5 + 48*x^4 + 124*x^3 + 80*x^2 + 65*x + 80, x^73 + 60*x^71 + 112*x^70 + 22*x^69 + 80*x^68 + 60*x^67 + 16*x^66 + 121*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 22*x^5 + 80*x^4 + 124*x^3 + 16*x^2 + 97*x + 48, x^73 + 60*x^71 + 4*x^70 + 110*x^69 + 12*x^68 + 12*x^67 + 92*x^66 + 81*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 110*x^5 + 76*x^4 + 76*x^3 + 28*x^2 + 57*x + 84, x^73 + 60*x^71 + 96*x^70 + 22*x^69 + 96*x^68 + 60*x^67 + 32*x^66 + 121*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 22*x^5 + 96*x^4 + 124*x^3 + 32*x^2 + 97*x + 32, x^73 + 60*x^71 + 116*x^70 + 46*x^69 + 92*x^68 + 76*x^67 + 44*x^66 + 81*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 46*x^5 + 28*x^4 + 12*x^3 + 108*x^2 + 57*x + 68, x^73 + 60*x^71 + 102*x^69 + 48*x^68 + 92*x^67 + 32*x^66 + 9*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 102*x^5 + 48*x^4 + 28*x^3 + 32*x^2 + 113*x + 48, x^73 + 60*x^71 + 120*x^70 + 6*x^69 + 88*x^68 + 28*x^67 + 40*x^66 + 41*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 6*x^5 + 88*x^4 + 92*x^3 + 40*x^2 + 17*x + 8, x^73 + 60*x^71 + 24*x^70 + 118*x^69 + 104*x^68 + 124*x^67 + 40*x^66 + 89*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 118*x^5 + 104*x^4 + 60*x^3 + 40*x^2 + 65*x + 88, x^73 + 60*x^71 + 68*x^70 + 30*x^69 + 92*x^68 + 44*x^67 + 60*x^66 + x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 30*x^5 + 28*x^4 + 108*x^3 + 124*x^2 + 105*x + 100, x^73 + 60*x^71 + 40*x^70 + 70*x^69 + 40*x^68 + 28*x^67 + 120*x^66 + 105*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 70*x^5 + 40*x^4 + 92*x^3 + 120*x^2 + 81*x + 56, x^73 + 60*x^71 + 20*x^70 + 62*x^69 + 76*x^68 + 44*x^67 + 44*x^66 + 97*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 62*x^5 + 12*x^4 + 108*x^3 + 108*x^2 + 73*x + 52, x^73 + 60*x^71 + 92*x^70 + 126*x^69 + 100*x^68 + 108*x^67 + 100*x^66 + 97*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 126*x^5 + 36*x^4 + 44*x^3 + 36*x^2 + 73*x + 28, x^73 + 60*x^71 + 76*x^70 + 46*x^69 + 68*x^68 + 76*x^67 + 84*x^66 + 81*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 46*x^5 + 4*x^4 + 12*x^3 + 20*x^2 + 57*x + 92, x^73 + 60*x^71 + 52*x^70 + 78*x^69 + 60*x^68 + 76*x^67 + 108*x^66 + 49*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 78*x^5 + 124*x^4 + 12*x^3 + 44*x^2 + 25*x + 100, x^73 + 60*x^71 + 92*x^70 + 30*x^69 + 68*x^68 + 108*x^67 + 100*x^66 + 65*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 30*x^5 + 4*x^4 + 44*x^3 + 36*x^2 + 41*x + 60, x^73 + 60*x^71 + 52*x^70 + 94*x^69 + 12*x^68 + 44*x^67 + 12*x^66 + 65*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 94*x^5 + 76*x^4 + 108*x^3 + 76*x^2 + 41*x + 116, x^73 + 60*x^71 + 76*x^70 + 30*x^69 + 20*x^68 + 44*x^67 + 52*x^66 + x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 30*x^5 + 84*x^4 + 108*x^3 + 116*x^2 + 105*x + 44, x^73 + 60*x^71 + 68*x^70 + 30*x^69 + 124*x^68 + 108*x^67 + 60*x^66 + 65*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 30*x^5 + 60*x^4 + 44*x^3 + 124*x^2 + 41*x + 68, x^73 + 60*x^71 + 44*x^70 + 126*x^69 + 116*x^68 + 108*x^67 + 84*x^66 + 97*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 126*x^5 + 52*x^4 + 44*x^3 + 20*x^2 + 73*x + 76, x^73 + 60*x^71 + 44*x^70 + 126*x^69 + 84*x^68 + 108*x^67 + 20*x^66 + 97*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 126*x^5 + 20*x^4 + 44*x^3 + 84*x^2 + 73*x + 44, x^73 + 60*x^71 + 52*x^70 + 110*x^69 + 124*x^68 + 76*x^67 + 44*x^66 + 17*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 110*x^5 + 60*x^4 + 12*x^3 + 108*x^2 + 121*x + 100, x^73 + 60*x^71 + 24*x^70 + 38*x^69 + 88*x^68 + 28*x^67 + 8*x^66 + 9*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 38*x^5 + 88*x^4 + 92*x^3 + 8*x^2 + 113*x + 8, x^73 + 60*x^71 + 52*x^70 + 126*x^69 + 44*x^68 + 44*x^67 + 12*x^66 + 33*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 126*x^5 + 108*x^4 + 108*x^3 + 76*x^2 + 9*x + 84, x^73 + 60*x^71 + 72*x^70 + 54*x^69 + 88*x^68 + 60*x^67 + 120*x^66 + 89*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 54*x^5 + 88*x^4 + 124*x^3 + 120*x^2 + 65*x + 104, x^73 + 60*x^71 + 96*x^70 + 70*x^69 + 16*x^68 + 28*x^67 + 64*x^66 + 105*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 70*x^5 + 16*x^4 + 92*x^3 + 64*x^2 + 81*x + 80, x^73 + 60*x^71 + 88*x^70 + 22*x^69 + 40*x^68 + 124*x^67 + 40*x^66 + 57*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 22*x^5 + 40*x^4 + 60*x^3 + 40*x^2 + 33*x + 88, x^73 + 60*x^71 + 116*x^70 + 110*x^69 + 60*x^68 + 12*x^67 + 44*x^66 + 81*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 110*x^5 + 124*x^4 + 76*x^3 + 108*x^2 + 57*x + 100, x^73 + 60*x^71 + 108*x^70 + 126*x^69 + 84*x^68 + 44*x^67 + 20*x^66 + 33*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 126*x^5 + 20*x^4 + 108*x^3 + 84*x^2 + 9*x + 108, x^73 + 60*x^71 + 80*x^70 + 38*x^69 + 28*x^67 + 80*x^66 + 9*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 38*x^5 + 92*x^3 + 80*x^2 + 113*x + 96, x^73 + 60*x^71 + 54*x^69 + 64*x^68 + 124*x^67 + 25*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 54*x^5 + 64*x^4 + 60*x^3 + x + 64, x^73 + 60*x^71 + 4*x^70 + 30*x^69 + 124*x^68 + 108*x^67 + 124*x^66 + 65*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 30*x^5 + 60*x^4 + 44*x^3 + 60*x^2 + 41*x + 68, x^73 + 60*x^71 + 72*x^70 + 38*x^69 + 40*x^68 + 28*x^67 + 88*x^66 + 9*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 38*x^5 + 40*x^4 + 92*x^3 + 88*x^2 + 113*x + 56, x^73 + 60*x^71 + 64*x^70 + 86*x^69 + 96*x^68 + 124*x^67 + 64*x^66 + 121*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 86*x^5 + 96*x^4 + 60*x^3 + 64*x^2 + 97*x + 32, x^73 + 60*x^71 + 48*x^70 + 86*x^69 + 80*x^68 + 60*x^67 + 80*x^66 + 57*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 86*x^5 + 80*x^4 + 124*x^3 + 80*x^2 + 33*x + 48, x^73 + 60*x^71 + 72*x^70 + 54*x^69 + 56*x^68 + 124*x^67 + 120*x^66 + 25*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 54*x^5 + 56*x^4 + 60*x^3 + 120*x^2 + x + 8, x^73 + 60*x^71 + 102*x^69 + 16*x^68 + 28*x^67 + 32*x^66 + 73*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 102*x^5 + 16*x^4 + 92*x^3 + 32*x^2 + 49*x + 80, x^73 + 60*x^71 + 24*x^70 + 70*x^69 + 120*x^68 + 92*x^67 + 72*x^66 + 41*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 70*x^5 + 120*x^4 + 28*x^3 + 72*x^2 + 17*x + 40, x^73 + 60*x^71 + 84*x^70 + 62*x^69 + 108*x^68 + 108*x^67 + 108*x^66 + 33*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 62*x^5 + 44*x^4 + 44*x^3 + 44*x^2 + 9*x + 20, x^73 + 60*x^71 + 100*x^70 + 14*x^69 + 12*x^68 + 76*x^67 + 60*x^66 + 113*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 14*x^5 + 76*x^4 + 12*x^3 + 124*x^2 + 89*x + 20, x^73 + 60*x^71 + 108*x^70 + 78*x^69 + 36*x^68 + 12*x^67 + 52*x^66 + 113*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 78*x^5 + 100*x^4 + 76*x^3 + 116*x^2 + 89*x + 124, x^73 + 60*x^71 + 28*x^70 + 30*x^69 + 36*x^68 + 108*x^67 + 100*x^66 + 65*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 30*x^5 + 100*x^4 + 44*x^3 + 36*x^2 + 41*x + 28, x^73 + 60*x^71 + 32*x^70 + 102*x^69 + 16*x^68 + 92*x^67 + 9*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 102*x^5 + 16*x^4 + 28*x^3 + 113*x + 80, x^73 + 60*x^71 + 28*x^70 + 126*x^69 + 100*x^68 + 44*x^67 + 100*x^66 + 33*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 126*x^5 + 36*x^4 + 108*x^3 + 36*x^2 + 9*x + 92, x^73 + 60*x^71 + 112*x^70 + 22*x^69 + 16*x^68 + 60*x^67 + 16*x^66 + 121*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 22*x^5 + 16*x^4 + 124*x^3 + 16*x^2 + 97*x + 112, x^73 + 60*x^71 + 72*x^70 + 22*x^69 + 120*x^68 + 60*x^67 + 120*x^66 + 121*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 22*x^5 + 120*x^4 + 124*x^3 + 120*x^2 + 97*x + 72, x^73 + 60*x^71 + 100*x^70 + 78*x^69 + 12*x^68 + 12*x^67 + 124*x^66 + 113*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 78*x^5 + 76*x^4 + 76*x^3 + 60*x^2 + 89*x + 84, x^73 + 60*x^71 + 52*x^70 + 14*x^69 + 28*x^68 + 76*x^67 + 44*x^66 + 113*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 14*x^5 + 92*x^4 + 12*x^3 + 108*x^2 + 89*x + 68, x^73 + 60*x^71 + 64*x^70 + 118*x^69 + 64*x^68 + 124*x^67 + 64*x^66 + 89*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 118*x^5 + 64*x^4 + 60*x^3 + 64*x^2 + 65*x + 64, x^73 + 60*x^71 + 76*x^70 + 62*x^69 + 52*x^68 + 108*x^67 + 116*x^66 + 33*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 62*x^5 + 116*x^4 + 44*x^3 + 52*x^2 + 9*x + 76, x^73 + 60*x^71 + 52*x^70 + 94*x^69 + 44*x^68 + 108*x^67 + 12*x^66 + x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 94*x^5 + 108*x^4 + 44*x^3 + 76*x^2 + 105*x + 84, x^73 + 60*x^71 + 52*x^70 + 30*x^69 + 108*x^68 + 44*x^67 + 76*x^66 + x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 30*x^5 + 44*x^4 + 108*x^3 + 12*x^2 + 105*x + 84, x^73 + 60*x^71 + 4*x^70 + 126*x^69 + 92*x^68 + 44*x^67 + 60*x^66 + 33*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 126*x^5 + 28*x^4 + 108*x^3 + 124*x^2 + 9*x + 36, x^73 + 60*x^71 + 44*x^70 + 62*x^69 + 116*x^68 + 108*x^67 + 84*x^66 + 33*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 62*x^5 + 52*x^4 + 44*x^3 + 20*x^2 + 9*x + 76, x^73 + 60*x^71 + 84*x^70 + 126*x^69 + 44*x^68 + 108*x^67 + 108*x^66 + 97*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 126*x^5 + 108*x^4 + 44*x^3 + 44*x^2 + 73*x + 84, x^73 + 60*x^71 + 124*x^70 + 126*x^69 + 68*x^68 + 44*x^67 + 4*x^66 + 33*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 126*x^5 + 4*x^4 + 108*x^3 + 68*x^2 + 9*x + 124, x^73 + 60*x^71 + 68*x^70 + 46*x^69 + 12*x^68 + 76*x^67 + 92*x^66 + 81*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 46*x^5 + 76*x^4 + 12*x^3 + 28*x^2 + 57*x + 20, x^73 + 60*x^71 + 102*x^69 + 112*x^68 + 92*x^67 + 32*x^66 + 9*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 102*x^5 + 112*x^4 + 28*x^3 + 32*x^2 + 113*x + 112, x^73 + 60*x^71 + 68*x^70 + 110*x^69 + 44*x^68 + 12*x^67 + 92*x^66 + 81*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 110*x^5 + 108*x^4 + 76*x^3 + 28*x^2 + 57*x + 116, x^73 + 60*x^71 + 36*x^70 + 126*x^69 + 92*x^68 + 108*x^67 + 28*x^66 + 97*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 126*x^5 + 28*x^4 + 44*x^3 + 92*x^2 + 73*x + 36, x^73 + 60*x^71 + 24*x^70 + 6*x^69 + 24*x^68 + 28*x^67 + 72*x^66 + 41*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 6*x^5 + 24*x^4 + 92*x^3 + 72*x^2 + 17*x + 8, x^73 + 60*x^71 + 124*x^70 + 46*x^69 + 20*x^68 + 12*x^67 + 100*x^66 + 17*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 46*x^5 + 84*x^4 + 76*x^3 + 36*x^2 + 121*x + 76, x^73 + 60*x^71 + 32*x^70 + 102*x^69 + 112*x^68 + 28*x^67 + 73*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 102*x^5 + 112*x^4 + 92*x^3 + 49*x + 112, x^73 + 60*x^71 + 16*x^70 + 118*x^69 + 48*x^68 + 60*x^67 + 48*x^66 + 25*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 118*x^5 + 48*x^4 + 124*x^3 + 48*x^2 + x + 16, x^73 + 60*x^71 + 64*x^70 + 102*x^69 + 48*x^68 + 92*x^67 + 96*x^66 + 9*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 102*x^5 + 48*x^4 + 28*x^3 + 96*x^2 + 113*x + 48, x^73 + 60*x^71 + 96*x^70 + 102*x^69 + 48*x^68 + 28*x^67 + 64*x^66 + 73*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 102*x^5 + 48*x^4 + 92*x^3 + 64*x^2 + 49*x + 48, x^73 + 60*x^71 + 72*x^70 + 70*x^69 + 72*x^68 + 28*x^67 + 88*x^66 + 105*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 70*x^5 + 72*x^4 + 92*x^3 + 88*x^2 + 81*x + 24, x^73 + 60*x^71 + 56*x^70 + 118*x^69 + 104*x^68 + 60*x^67 + 8*x^66 + 25*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 118*x^5 + 104*x^4 + 124*x^3 + 8*x^2 + x + 88, x^73 + 60*x^71 + 108*x^70 + 126*x^69 + 20*x^68 + 44*x^67 + 20*x^66 + 33*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 126*x^5 + 84*x^4 + 108*x^3 + 84*x^2 + 9*x + 44, x^73 + 60*x^71 + 32*x^70 + 22*x^69 + 64*x^68 + 124*x^67 + 96*x^66 + 57*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 22*x^5 + 64*x^4 + 60*x^3 + 96*x^2 + 33*x + 64, x^73 + 60*x^71 + 20*x^70 + 110*x^69 + 60*x^68 + 12*x^67 + 76*x^66 + 81*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 110*x^5 + 124*x^4 + 76*x^3 + 12*x^2 + 57*x + 36, x^73 + 60*x^71 + 76*x^70 + 126*x^69 + 84*x^68 + 44*x^67 + 116*x^66 + 33*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 126*x^5 + 20*x^4 + 108*x^3 + 52*x^2 + 9*x + 44, x^73 + 60*x^71 + 92*x^70 + 30*x^69 + 100*x^68 + 108*x^67 + 36*x^66 + 65*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 30*x^5 + 36*x^4 + 44*x^3 + 100*x^2 + 41*x + 92, x^73 + 60*x^71 + 22*x^69 + 64*x^68 + 60*x^67 + 121*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 22*x^5 + 64*x^4 + 124*x^3 + 97*x + 64, x^73 + 60*x^71 + 68*x^70 + 78*x^69 + 12*x^68 + 76*x^67 + 28*x^66 + 49*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 78*x^5 + 76*x^4 + 12*x^3 + 92*x^2 + 25*x + 84, x^73 + 60*x^71 + 38*x^69 + 80*x^68 + 92*x^67 + 96*x^66 + 73*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 38*x^5 + 80*x^4 + 28*x^3 + 96*x^2 + 49*x + 80, x^73 + 60*x^71 + 84*x^70 + 62*x^69 + 44*x^68 + 108*x^67 + 108*x^66 + 33*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 62*x^5 + 108*x^4 + 44*x^3 + 44*x^2 + 9*x + 84, x^73 + 60*x^71 + 20*x^70 + 94*x^69 + 108*x^68 + 108*x^67 + 108*x^66 + x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 94*x^5 + 44*x^4 + 44*x^3 + 44*x^2 + 105*x + 84, x^73 + 60*x^71 + 48*x^70 + 102*x^69 + 64*x^68 + 28*x^67 + 48*x^66 + 73*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 102*x^5 + 64*x^4 + 92*x^3 + 48*x^2 + 49*x + 96, x^73 + 60*x^71 + 16*x^70 + 86*x^69 + 16*x^68 + 124*x^67 + 112*x^66 + 121*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 86*x^5 + 16*x^4 + 60*x^3 + 112*x^2 + 97*x + 112, x^73 + 60*x^71 + 32*x^70 + 102*x^69 + 80*x^68 + 92*x^67 + 9*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 102*x^5 + 80*x^4 + 28*x^3 + 113*x + 16, x^73 + 60*x^71 + 8*x^70 + 6*x^69 + 40*x^68 + 28*x^67 + 88*x^66 + 41*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 6*x^5 + 40*x^4 + 92*x^3 + 88*x^2 + 17*x + 120, x^73 + 60*x^71 + 104*x^70 + 102*x^69 + 104*x^68 + 28*x^67 + 120*x^66 + 73*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 102*x^5 + 104*x^4 + 92*x^3 + 120*x^2 + 49*x + 56, x^73 + 60*x^71 + 124*x^70 + 30*x^69 + 4*x^68 + 44*x^67 + 68*x^66 + x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 30*x^5 + 68*x^4 + 108*x^3 + 4*x^2 + 105*x + 124, x^73 + 60*x^71 + 100*x^70 + 14*x^69 + 108*x^68 + 12*x^67 + 60*x^66 + 49*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 14*x^5 + 44*x^4 + 76*x^3 + 124*x^2 + 25*x + 52, x^73 + 60*x^71 + 36*x^70 + 94*x^69 + 28*x^68 + 108*x^67 + 92*x^66 + x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 94*x^5 + 92*x^4 + 44*x^3 + 28*x^2 + 105*x + 36, x^73 + 60*x^71 + 68*x^70 + 110*x^69 + 44*x^68 + 76*x^67 + 28*x^66 + 17*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 110*x^5 + 108*x^4 + 12*x^3 + 92*x^2 + 121*x + 52, x^73 + 60*x^71 + 96*x^70 + 54*x^69 + 124*x^67 + 96*x^66 + 25*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 54*x^5 + 60*x^3 + 96*x^2 + x + 64, x^73 + 60*x^71 + 52*x^70 + 126*x^69 + 76*x^68 + 44*x^67 + 76*x^66 + 33*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 126*x^5 + 12*x^4 + 108*x^3 + 12*x^2 + 9*x + 116, x^73 + 60*x^71 + 52*x^70 + 78*x^69 + 28*x^68 + 12*x^67 + 108*x^66 + 113*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 78*x^5 + 92*x^4 + 76*x^3 + 44*x^2 + 89*x + 4, x^73 + 60*x^71 + 68*x^70 + 30*x^69 + 28*x^68 + 108*x^67 + 124*x^66 + 65*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 30*x^5 + 92*x^4 + 44*x^3 + 60*x^2 + 41*x + 100, x^73 + 60*x^71 + 48*x^70 + 118*x^69 + 112*x^68 + 124*x^67 + 16*x^66 + 89*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 118*x^5 + 112*x^4 + 60*x^3 + 16*x^2 + 65*x + 80, x^73 + 60*x^71 + 76*x^70 + 46*x^69 + 100*x^68 + 12*x^67 + 84*x^66 + 17*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 46*x^5 + 36*x^4 + 76*x^3 + 20*x^2 + 121*x + 60, x^73 + 60*x^71 + 108*x^70 + 110*x^69 + 4*x^68 + 76*x^67 + 116*x^66 + 17*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 110*x^5 + 68*x^4 + 12*x^3 + 52*x^2 + 121*x + 92, x^73 + 60*x^71 + 44*x^70 + 62*x^69 + 52*x^68 + 108*x^67 + 84*x^66 + 33*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 62*x^5 + 116*x^4 + 44*x^3 + 20*x^2 + 9*x + 12, x^73 + 60*x^71 + 68*x^70 + 62*x^69 + 60*x^68 + 44*x^67 + 60*x^66 + 97*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 62*x^5 + 124*x^4 + 108*x^3 + 124*x^2 + 73*x + 4, x^73 + 60*x^71 + 36*x^70 + 14*x^69 + 108*x^68 + 12*x^67 + 124*x^66 + 49*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 14*x^5 + 44*x^4 + 76*x^3 + 60*x^2 + 25*x + 52, x^73 + 60*x^71 + 116*x^70 + 94*x^69 + 12*x^68 + 44*x^67 + 76*x^66 + 65*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 94*x^5 + 76*x^4 + 108*x^3 + 12*x^2 + 41*x + 116, x^73 + 60*x^71 + 92*x^70 + 110*x^69 + 84*x^68 + 12*x^67 + 68*x^66 + 81*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 110*x^5 + 20*x^4 + 76*x^3 + 4*x^2 + 57*x + 76, x^73 + 60*x^71 + 116*x^70 + 62*x^69 + 108*x^68 + 108*x^67 + 12*x^66 + 33*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 62*x^5 + 44*x^4 + 44*x^3 + 76*x^2 + 9*x + 84, x^73 + 60*x^71 + 32*x^70 + 54*x^69 + 64*x^68 + 124*x^67 + 32*x^66 + 25*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 54*x^5 + 64*x^4 + 60*x^3 + 32*x^2 + x, x^73 + 60*x^71 + 54*x^69 + 32*x^68 + 60*x^67 + 89*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 54*x^5 + 32*x^4 + 124*x^3 + 65*x + 96, x^73 + 60*x^71 + 48*x^70 + 22*x^69 + 112*x^68 + 60*x^67 + 16*x^66 + 121*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 22*x^5 + 112*x^4 + 124*x^3 + 16*x^2 + 97*x + 80, x^73 + 60*x^71 + 40*x^70 + 118*x^69 + 120*x^68 + 124*x^67 + 88*x^66 + 89*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 118*x^5 + 120*x^4 + 60*x^3 + 88*x^2 + 65*x + 8, x^73 + 60*x^71 + 72*x^70 + 22*x^69 + 120*x^68 + 124*x^67 + 56*x^66 + 57*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 22*x^5 + 120*x^4 + 60*x^3 + 56*x^2 + 33*x + 8, x^73 + 60*x^71 + 68*x^70 + 30*x^69 + 124*x^68 + 44*x^67 + 124*x^66 + x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 30*x^5 + 60*x^4 + 108*x^3 + 60*x^2 + 105*x + 4, x^73 + 60*x^71 + 84*x^70 + 30*x^69 + 44*x^68 + 108*x^67 + 44*x^66 + 65*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 30*x^5 + 108*x^4 + 44*x^3 + 108*x^2 + 41*x + 20, x^73 + 60*x^71 + 52*x^70 + 78*x^69 + 60*x^68 + 12*x^67 + 44*x^66 + 113*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 78*x^5 + 124*x^4 + 76*x^3 + 108*x^2 + 89*x + 36, x^73 + 60*x^71 + 28*x^70 + 62*x^69 + 4*x^68 + 108*x^67 + 100*x^66 + 33*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 62*x^5 + 68*x^4 + 44*x^3 + 36*x^2 + 9*x + 60, x^73 + 60*x^71 + 100*x^70 + 78*x^69 + 108*x^68 + 12*x^67 + 60*x^66 + 113*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 78*x^5 + 44*x^4 + 76*x^3 + 124*x^2 + 89*x + 52, x^73 + 60*x^71 + 56*x^70 + 54*x^69 + 72*x^68 + 124*x^67 + 8*x^66 + 25*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 54*x^5 + 72*x^4 + 60*x^3 + 8*x^2 + x + 120, x^73 + 60*x^71 + 28*x^70 + 110*x^69 + 52*x^68 + 76*x^67 + 4*x^66 + 17*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 110*x^5 + 116*x^4 + 12*x^3 + 68*x^2 + 121*x + 108, x^73 + 60*x^71 + 104*x^70 + 54*x^69 + 56*x^68 + 124*x^67 + 24*x^66 + 25*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 54*x^5 + 56*x^4 + 60*x^3 + 24*x^2 + x + 72, x^73 + 60*x^71 + 104*x^70 + 86*x^69 + 88*x^68 + 60*x^67 + 88*x^66 + 57*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 86*x^5 + 88*x^4 + 124*x^3 + 88*x^2 + 33*x + 104, x^73 + 60*x^71 + 28*x^70 + 62*x^69 + 100*x^68 + 108*x^67 + 36*x^66 + 33*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 62*x^5 + 36*x^4 + 44*x^3 + 100*x^2 + 9*x + 28, x^73 + 60*x^71 + 28*x^70 + 94*x^69 + 4*x^68 + 108*x^67 + 36*x^66 + x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 94*x^5 + 68*x^4 + 44*x^3 + 100*x^2 + 105*x + 124, x^73 + 60*x^71 + 20*x^70 + 126*x^69 + 12*x^68 + 108*x^67 + 108*x^66 + 97*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 126*x^5 + 76*x^4 + 44*x^3 + 44*x^2 + 73*x + 52, x^73 + 60*x^71 + 80*x^70 + 118*x^69 + 16*x^68 + 60*x^67 + 48*x^66 + 25*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 118*x^5 + 16*x^4 + 124*x^3 + 48*x^2 + x + 112, x^73 + 60*x^71 + 96*x^70 + 22*x^69 + 60*x^67 + 96*x^66 + 121*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 22*x^5 + 124*x^3 + 96*x^2 + 97*x + 64, x^73 + 60*x^71 + 80*x^70 + 86*x^69 + 16*x^68 + 124*x^67 + 48*x^66 + 121*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 86*x^5 + 16*x^4 + 60*x^3 + 48*x^2 + 97*x + 112, x^73 + 60*x^71 + 40*x^70 + 6*x^69 + 104*x^68 + 92*x^67 + 56*x^66 + 105*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 6*x^5 + 104*x^4 + 28*x^3 + 56*x^2 + 81*x + 56, x^73 + 60*x^71 + 96*x^70 + 86*x^69 + 96*x^68 + 124*x^67 + 96*x^66 + 121*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 86*x^5 + 96*x^4 + 60*x^3 + 96*x^2 + 97*x + 96, x^73 + 60*x^71 + 40*x^70 + 22*x^69 + 88*x^68 + 60*x^67 + 24*x^66 + 121*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 22*x^5 + 88*x^4 + 124*x^3 + 24*x^2 + 97*x + 104, x^73 + 60*x^71 + 24*x^70 + 118*x^69 + 40*x^68 + 124*x^67 + 40*x^66 + 89*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 118*x^5 + 40*x^4 + 60*x^3 + 40*x^2 + 65*x + 24, x^73 + 60*x^71 + 24*x^70 + 6*x^69 + 88*x^68 + 28*x^67 + 72*x^66 + 41*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 6*x^5 + 88*x^4 + 92*x^3 + 72*x^2 + 17*x + 72, x^73 + 60*x^71 + 92*x^70 + 46*x^69 + 84*x^68 + 12*x^67 + 68*x^66 + 17*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 46*x^5 + 20*x^4 + 76*x^3 + 4*x^2 + 121*x + 76, x^73 + 60*x^71 + 32*x^70 + 22*x^69 + 64*x^68 + 60*x^67 + 32*x^66 + 121*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 22*x^5 + 64*x^4 + 124*x^3 + 32*x^2 + 97*x, x^73 + 60*x^71 + 16*x^70 + 38*x^69 + 32*x^68 + 28*x^67 + 80*x^66 + 9*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 38*x^5 + 32*x^4 + 92*x^3 + 80*x^2 + 113*x, x^73 + 60*x^71 + 118*x^69 + 96*x^68 + 60*x^67 + 25*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 118*x^5 + 96*x^4 + 124*x^3 + x + 32, x^73 + 60*x^71 + 44*x^70 + 78*x^69 + 4*x^68 + 76*x^67 + 116*x^66 + 49*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 78*x^5 + 68*x^4 + 12*x^3 + 52*x^2 + 25*x + 28, x^73 + 60*x^71 + 12*x^70 + 78*x^69 + 4*x^68 + 12*x^67 + 20*x^66 + 113*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 78*x^5 + 68*x^4 + 76*x^3 + 84*x^2 + 89*x + 28, x^73 + 60*x^71 + 84*x^70 + 78*x^69 + 60*x^68 + 76*x^67 + 12*x^66 + 49*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 78*x^5 + 124*x^4 + 12*x^3 + 76*x^2 + 25*x + 36, x^73 + 60*x^71 + 72*x^70 + 38*x^69 + 72*x^68 + 92*x^67 + 88*x^66 + 73*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 38*x^5 + 72*x^4 + 28*x^3 + 88*x^2 + 49*x + 24, x^73 + 60*x^71 + 68*x^70 + 30*x^69 + 60*x^68 + 44*x^67 + 124*x^66 + x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 30*x^5 + 124*x^4 + 108*x^3 + 60*x^2 + 105*x + 68, x^73 + 60*x^71 + 84*x^70 + 126*x^69 + 76*x^68 + 108*x^67 + 44*x^66 + 97*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 126*x^5 + 12*x^4 + 44*x^3 + 108*x^2 + 73*x + 116, x^73 + 60*x^71 + 4*x^70 + 30*x^69 + 60*x^68 + 44*x^67 + 60*x^66 + x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 30*x^5 + 124*x^4 + 108*x^3 + 124*x^2 + 105*x + 68, x^73 + 60*x^71 + 124*x^70 + 46*x^69 + 116*x^68 + 12*x^67 + 36*x^66 + 17*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 46*x^5 + 52*x^4 + 76*x^3 + 100*x^2 + 121*x + 44, x^73 + 60*x^71 + 48*x^70 + 38*x^69 + 96*x^68 + 92*x^67 + 48*x^66 + 73*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 38*x^5 + 96*x^4 + 28*x^3 + 48*x^2 + 49*x + 64, x^73 + 60*x^71 + 4*x^70 + 78*x^69 + 108*x^68 + 76*x^67 + 28*x^66 + 49*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 78*x^5 + 44*x^4 + 12*x^3 + 92*x^2 + 25*x + 52, x^73 + 60*x^71 + 108*x^70 + 46*x^69 + 4*x^68 + 12*x^67 + 52*x^66 + 17*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 46*x^5 + 68*x^4 + 76*x^3 + 116*x^2 + 121*x + 28, x^73 + 60*x^71 + 20*x^70 + 62*x^69 + 44*x^68 + 108*x^67 + 44*x^66 + 33*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 62*x^5 + 108*x^4 + 44*x^3 + 108*x^2 + 9*x + 84, x^73 + 60*x^71 + 104*x^70 + 70*x^69 + 72*x^68 + 28*x^67 + 120*x^66 + 105*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 70*x^5 + 72*x^4 + 92*x^3 + 120*x^2 + 81*x + 88, x^73 + 60*x^71 + 60*x^70 + 14*x^69 + 20*x^68 + 12*x^67 + 100*x^66 + 49*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 14*x^5 + 84*x^4 + 76*x^3 + 36*x^2 + 25*x + 12, x^73 + 60*x^71 + 124*x^70 + 126*x^69 + 4*x^68 + 108*x^67 + 68*x^66 + 97*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 126*x^5 + 68*x^4 + 44*x^3 + 4*x^2 + 73*x + 124, x^73 + 60*x^71 + 68*x^70 + 110*x^69 + 12*x^68 + 12*x^67 + 28*x^66 + 81*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 110*x^5 + 76*x^4 + 76*x^3 + 92*x^2 + 57*x + 84, x^73 + 60*x^71 + 52*x^70 + 46*x^69 + 28*x^68 + 12*x^67 + 44*x^66 + 17*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 46*x^5 + 92*x^4 + 76*x^3 + 108*x^2 + 121*x + 68, x^73 + 60*x^71 + 80*x^70 + 38*x^69 + 92*x^67 + 16*x^66 + 73*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 38*x^5 + 28*x^3 + 16*x^2 + 49*x + 32, x^73 + 60*x^71 + 48*x^70 + 54*x^69 + 16*x^68 + 60*x^67 + 16*x^66 + 89*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 54*x^5 + 16*x^4 + 124*x^3 + 16*x^2 + 65*x + 48, x^73 + 60*x^71 + 72*x^70 + 86*x^69 + 24*x^68 + 124*x^67 + 120*x^66 + 121*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 86*x^5 + 24*x^4 + 60*x^3 + 120*x^2 + 97*x + 40, x^73 + 60*x^71 + 118*x^69 + 60*x^67 + 64*x^66 + 25*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 118*x^5 + 124*x^3 + 64*x^2 + x + 64, x^73 + 60*x^71 + 92*x^70 + 62*x^69 + 36*x^68 + 108*x^67 + 100*x^66 + 33*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 62*x^5 + 100*x^4 + 44*x^3 + 36*x^2 + 9*x + 92, x^73 + 60*x^71 + 4*x^70 + 78*x^69 + 12*x^68 + 12*x^67 + 28*x^66 + 113*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 78*x^5 + 76*x^4 + 76*x^3 + 92*x^2 + 89*x + 20, x^73 + 60*x^71 + 100*x^70 + 30*x^69 + 92*x^68 + 108*x^67 + 28*x^66 + 65*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 30*x^5 + 28*x^4 + 44*x^3 + 92*x^2 + 41*x + 100, x^73 + 60*x^71 + 100*x^70 + 126*x^69 + 60*x^68 + 44*x^67 + 92*x^66 + 33*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 126*x^5 + 124*x^4 + 108*x^3 + 28*x^2 + 9*x + 68, x^73 + 60*x^71 + 116*x^70 + 30*x^69 + 44*x^68 + 108*x^67 + 76*x^66 + 65*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 30*x^5 + 108*x^4 + 44*x^3 + 12*x^2 + 41*x + 84, x^73 + 60*x^71 + 120*x^70 + 6*x^69 + 24*x^68 + 92*x^67 + 104*x^66 + 105*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 6*x^5 + 24*x^4 + 28*x^3 + 104*x^2 + 81*x + 8, x^73 + 60*x^71 + 32*x^70 + 118*x^69 + 32*x^68 + 124*x^67 + 96*x^66 + 89*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 118*x^5 + 32*x^4 + 60*x^3 + 96*x^2 + 65*x + 96, x^73 + 60*x^71 + 108*x^70 + 62*x^69 + 52*x^68 + 108*x^67 + 20*x^66 + 33*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 62*x^5 + 116*x^4 + 44*x^3 + 84*x^2 + 9*x + 12, x^73 + 60*x^71 + 80*x^70 + 38*x^69 + 64*x^68 + 92*x^67 + 16*x^66 + 73*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 38*x^5 + 64*x^4 + 28*x^3 + 16*x^2 + 49*x + 96, x^73 + 60*x^71 + 44*x^70 + 126*x^69 + 52*x^68 + 44*x^67 + 20*x^66 + 33*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 126*x^5 + 116*x^4 + 108*x^3 + 84*x^2 + 9*x + 76, x^73 + 60*x^71 + 24*x^70 + 102*x^69 + 56*x^68 + 28*x^67 + 72*x^66 + 73*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 102*x^5 + 56*x^4 + 92*x^3 + 72*x^2 + 49*x + 104, x^73 + 60*x^71 + 96*x^70 + 86*x^69 + 96*x^68 + 60*x^67 + 32*x^66 + 57*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 86*x^5 + 96*x^4 + 124*x^3 + 32*x^2 + 33*x + 32, x^73 + 60*x^71 + 20*x^70 + 94*x^69 + 12*x^68 + 108*x^67 + 44*x^66 + x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 94*x^5 + 76*x^4 + 44*x^3 + 108*x^2 + 105*x + 116, x^73 + 60*x^71 + 28*x^70 + 30*x^69 + 68*x^68 + 108*x^67 + 36*x^66 + 65*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 30*x^5 + 4*x^4 + 44*x^3 + 100*x^2 + 41*x + 60, x^73 + 60*x^71 + 104*x^70 + 118*x^69 + 24*x^68 + 124*x^67 + 88*x^66 + 89*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 118*x^5 + 24*x^4 + 60*x^3 + 88*x^2 + 65*x + 40, x^73 + 60*x^71 + 120*x^70 + 70*x^69 + 24*x^68 + 28*x^67 + 40*x^66 + 105*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 70*x^5 + 24*x^4 + 92*x^3 + 40*x^2 + 81*x + 72, x^73 + 60*x^71 + 40*x^70 + 22*x^69 + 24*x^68 + 124*x^67 + 88*x^66 + 57*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 22*x^5 + 24*x^4 + 60*x^3 + 88*x^2 + 33*x + 104, x^73 + 60*x^71 + 60*x^70 + 46*x^69 + 116*x^68 + 12*x^67 + 100*x^66 + 17*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 46*x^5 + 52*x^4 + 76*x^3 + 36*x^2 + 121*x + 44, x^73 + 60*x^71 + 28*x^70 + 14*x^69 + 116*x^68 + 12*x^67 + 4*x^66 + 49*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 14*x^5 + 52*x^4 + 76*x^3 + 68*x^2 + 25*x + 44, x^73 + 60*x^71 + 16*x^70 + 38*x^69 + 96*x^68 + 28*x^67 + 80*x^66 + 9*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 38*x^5 + 96*x^4 + 92*x^3 + 80*x^2 + 113*x + 64, x^73 + 60*x^71 + 56*x^70 + 22*x^69 + 8*x^68 + 124*x^67 + 72*x^66 + 57*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 22*x^5 + 8*x^4 + 60*x^3 + 72*x^2 + 33*x + 120, x^73 + 60*x^71 + 48*x^70 + 118*x^69 + 48*x^68 + 60*x^67 + 80*x^66 + 25*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 118*x^5 + 48*x^4 + 124*x^3 + 80*x^2 + x + 80, x^73 + 60*x^71 + 116*x^70 + 46*x^69 + 60*x^68 + 12*x^67 + 44*x^66 + 17*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 46*x^5 + 124*x^4 + 76*x^3 + 108*x^2 + 121*x + 100, x^73 + 60*x^71 + 104*x^70 + 102*x^69 + 8*x^68 + 28*x^67 + 56*x^66 + 73*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 102*x^5 + 8*x^4 + 92*x^3 + 56*x^2 + 49*x + 88, x^73 + 60*x^71 + 4*x^70 + 30*x^69 + 124*x^68 + 44*x^67 + 60*x^66 + x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 30*x^5 + 60*x^4 + 108*x^3 + 124*x^2 + 105*x + 4, x^73 + 60*x^71 + 120*x^70 + 70*x^69 + 88*x^68 + 28*x^67 + 40*x^66 + 105*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 70*x^5 + 88*x^4 + 92*x^3 + 40*x^2 + 81*x + 8, x^73 + 60*x^71 + 8*x^70 + 54*x^69 + 56*x^68 + 124*x^67 + 56*x^66 + 25*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 54*x^5 + 56*x^4 + 60*x^3 + 56*x^2 + x + 8, x^73 + 60*x^71 + 108*x^70 + 46*x^69 + 68*x^68 + 76*x^67 + 116*x^66 + 81*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 46*x^5 + 4*x^4 + 12*x^3 + 52*x^2 + 57*x + 28, x^73 + 60*x^71 + 8*x^70 + 102*x^69 + 40*x^68 + 92*x^67 + 88*x^66 + 9*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 102*x^5 + 40*x^4 + 28*x^3 + 88*x^2 + 113*x + 120, x^73 + 60*x^71 + 76*x^70 + 126*x^69 + 20*x^68 + 44*x^67 + 116*x^66 + 33*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 126*x^5 + 84*x^4 + 108*x^3 + 52*x^2 + 9*x + 108, x^73 + 60*x^71 + 124*x^70 + 110*x^69 + 116*x^68 + 12*x^67 + 36*x^66 + 81*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 110*x^5 + 52*x^4 + 76*x^3 + 100*x^2 + 57*x + 44, x^73 + 60*x^71 + 28*x^70 + 94*x^69 + 36*x^68 + 108*x^67 + 100*x^66 + x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 94*x^5 + 100*x^4 + 44*x^3 + 36*x^2 + 105*x + 28, x^73 + 60*x^71 + 20*x^70 + 14*x^69 + 60*x^68 + 76*x^67 + 76*x^66 + 113*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 14*x^5 + 124*x^4 + 12*x^3 + 12*x^2 + 89*x + 36, x^73 + 60*x^71 + 8*x^70 + 22*x^69 + 120*x^68 + 60*x^67 + 56*x^66 + 121*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 22*x^5 + 120*x^4 + 124*x^3 + 56*x^2 + 97*x + 72, x^73 + 60*x^71 + 112*x^70 + 54*x^69 + 112*x^68 + 60*x^67 + 16*x^66 + 89*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 54*x^5 + 112*x^4 + 124*x^3 + 16*x^2 + 65*x + 16, x^73 + 60*x^71 + 20*x^70 + 126*x^69 + 108*x^68 + 44*x^67 + 108*x^66 + 33*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 126*x^5 + 44*x^4 + 108*x^3 + 44*x^2 + 9*x + 84, x^73 + 60*x^71 + 56*x^70 + 118*x^69 + 8*x^68 + 60*x^67 + 72*x^66 + 25*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 118*x^5 + 8*x^4 + 124*x^3 + 72*x^2 + x + 120, x^73 + 60*x^71 + 20*x^70 + 110*x^69 + 92*x^68 + 12*x^67 + 12*x^66 + 81*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 110*x^5 + 28*x^4 + 76*x^3 + 76*x^2 + 57*x + 68, x^73 + 60*x^71 + 44*x^70 + 110*x^69 + 36*x^68 + 76*x^67 + 116*x^66 + 17*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 110*x^5 + 100*x^4 + 12*x^3 + 52*x^2 + 121*x + 124, x^73 + 60*x^71 + 60*x^70 + 62*x^69 + 100*x^68 + 44*x^67 + 4*x^66 + 97*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 62*x^5 + 36*x^4 + 108*x^3 + 68*x^2 + 73*x + 28, x^73 + 60*x^71 + 40*x^70 + 102*x^69 + 40*x^68 + 28*x^67 + 56*x^66 + 73*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 102*x^5 + 40*x^4 + 92*x^3 + 56*x^2 + 49*x + 120, x^73 + 60*x^71 + 20*x^70 + 62*x^69 + 108*x^68 + 108*x^67 + 44*x^66 + 33*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 62*x^5 + 44*x^4 + 44*x^3 + 108*x^2 + 9*x + 20, x^73 + 60*x^71 + 124*x^70 + 126*x^69 + 4*x^68 + 44*x^67 + 4*x^66 + 33*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 126*x^5 + 68*x^4 + 108*x^3 + 68*x^2 + 9*x + 60, x^73 + 60*x^71 + 68*x^70 + 14*x^69 + 108*x^68 + 12*x^67 + 28*x^66 + 49*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 14*x^5 + 44*x^4 + 76*x^3 + 92*x^2 + 25*x + 116, x^73 + 60*x^71 + 52*x^70 + 78*x^69 + 124*x^68 + 76*x^67 + 108*x^66 + 49*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 78*x^5 + 60*x^4 + 12*x^3 + 44*x^2 + 25*x + 36, x^73 + 60*x^71 + 56*x^70 + 118*x^69 + 40*x^68 + 60*x^67 + 8*x^66 + 25*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 118*x^5 + 40*x^4 + 124*x^3 + 8*x^2 + x + 24, x^73 + 60*x^71 + 4*x^70 + 94*x^69 + 60*x^68 + 44*x^67 + 60*x^66 + 65*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 94*x^5 + 124*x^4 + 108*x^3 + 124*x^2 + 41*x + 68, x^73 + 60*x^71 + 68*x^70 + 126*x^69 + 92*x^68 + 44*x^67 + 124*x^66 + 33*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 126*x^5 + 28*x^4 + 108*x^3 + 60*x^2 + 9*x + 36, x^73 + 60*x^71 + 52*x^70 + 30*x^69 + 108*x^68 + 108*x^67 + 12*x^66 + 65*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 30*x^5 + 44*x^4 + 44*x^3 + 76*x^2 + 41*x + 20, x^73 + 60*x^71 + 60*x^70 + 46*x^69 + 20*x^68 + 12*x^67 + 36*x^66 + 17*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 46*x^5 + 84*x^4 + 76*x^3 + 100*x^2 + 121*x + 76, x^73 + 60*x^71 + 108*x^70 + 126*x^69 + 116*x^68 + 44*x^67 + 84*x^66 + 33*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 126*x^5 + 52*x^4 + 108*x^3 + 20*x^2 + 9*x + 12, x^73 + 60*x^71 + 76*x^70 + 30*x^69 + 52*x^68 + 108*x^67 + 52*x^66 + 65*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 30*x^5 + 116*x^4 + 44*x^3 + 116*x^2 + 41*x + 12, x^73 + 60*x^71 + 116*x^70 + 94*x^69 + 76*x^68 + 44*x^67 + 76*x^66 + 65*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 94*x^5 + 12*x^4 + 108*x^3 + 12*x^2 + 41*x + 52, x^73 + 60*x^71 + 76*x^70 + 126*x^69 + 52*x^68 + 108*x^67 + 116*x^66 + 97*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 126*x^5 + 116*x^4 + 44*x^3 + 52*x^2 + 73*x + 76, x^73 + 60*x^71 + 80*x^70 + 70*x^69 + 32*x^68 + 92*x^67 + 16*x^66 + 41*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 70*x^5 + 32*x^4 + 28*x^3 + 16*x^2 + 17*x, x^73 + 60*x^71 + 124*x^70 + 62*x^69 + 36*x^68 + 108*x^67 + 4*x^66 + 33*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 62*x^5 + 100*x^4 + 44*x^3 + 68*x^2 + 9*x + 28, x^73 + 60*x^71 + 52*x^70 + 14*x^69 + 60*x^68 + 76*x^67 + 108*x^66 + 113*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 14*x^5 + 124*x^4 + 12*x^3 + 44*x^2 + 89*x + 100, x^73 + 60*x^71 + 32*x^70 + 86*x^69 + 32*x^68 + 124*x^67 + 32*x^66 + 121*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 86*x^5 + 32*x^4 + 60*x^3 + 32*x^2 + 97*x + 32, x^73 + 60*x^71 + 8*x^70 + 38*x^69 + 8*x^68 + 28*x^67 + 88*x^66 + 9*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 38*x^5 + 8*x^4 + 92*x^3 + 88*x^2 + 113*x + 24, x^73 + 60*x^71 + 88*x^70 + 22*x^69 + 104*x^68 + 124*x^67 + 40*x^66 + 57*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 22*x^5 + 104*x^4 + 60*x^3 + 40*x^2 + 33*x + 24, x^73 + 60*x^71 + 84*x^70 + 110*x^69 + 60*x^68 + 12*x^67 + 12*x^66 + 81*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 110*x^5 + 124*x^4 + 76*x^3 + 76*x^2 + 57*x + 36, x^73 + 60*x^71 + 120*x^70 + 86*x^69 + 40*x^68 + 60*x^67 + 8*x^66 + 57*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 86*x^5 + 40*x^4 + 124*x^3 + 8*x^2 + 33*x + 88, x^73 + 60*x^71 + 68*x^70 + 78*x^69 + 108*x^68 + 12*x^67 + 28*x^66 + 113*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 78*x^5 + 44*x^4 + 76*x^3 + 92*x^2 + 89*x + 116, x^73 + 60*x^71 + 12*x^70 + 62*x^69 + 84*x^68 + 44*x^67 + 52*x^66 + 97*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 62*x^5 + 20*x^4 + 108*x^3 + 116*x^2 + 73*x + 44, x^73 + 60*x^71 + 80*x^70 + 38*x^69 + 96*x^68 + 28*x^67 + 16*x^66 + 9*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 38*x^5 + 96*x^4 + 92*x^3 + 16*x^2 + 113*x + 64, x^73 + 60*x^71 + 24*x^70 + 70*x^69 + 24*x^68 + 28*x^67 + 72*x^66 + 105*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 70*x^5 + 24*x^4 + 92*x^3 + 72*x^2 + 81*x + 8, x^73 + 60*x^71 + 24*x^70 + 70*x^69 + 56*x^68 + 92*x^67 + 72*x^66 + 41*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 70*x^5 + 56*x^4 + 28*x^3 + 72*x^2 + 17*x + 104, x^73 + 60*x^71 + 104*x^70 + 86*x^69 + 120*x^68 + 124*x^67 + 88*x^66 + 121*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 86*x^5 + 120*x^4 + 60*x^3 + 88*x^2 + 97*x + 72, x^73 + 60*x^71 + 112*x^70 + 22*x^69 + 112*x^68 + 60*x^67 + 80*x^66 + 121*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 22*x^5 + 112*x^4 + 124*x^3 + 80*x^2 + 97*x + 80, x^73 + 60*x^71 + 16*x^70 + 70*x^69 + 32*x^68 + 92*x^67 + 80*x^66 + 41*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 70*x^5 + 32*x^4 + 28*x^3 + 80*x^2 + 17*x, x^73 + 60*x^71 + 108*x^70 + 46*x^69 + 100*x^68 + 12*x^67 + 116*x^66 + 17*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 46*x^5 + 36*x^4 + 76*x^3 + 52*x^2 + 121*x + 124, x^73 + 60*x^71 + 4*x^70 + 110*x^69 + 108*x^68 + 12*x^67 + 28*x^66 + 81*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 110*x^5 + 44*x^4 + 76*x^3 + 92*x^2 + 57*x + 52, x^73 + 60*x^71 + 4*x^70 + 46*x^69 + 12*x^68 + 12*x^67 + 92*x^66 + 17*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 46*x^5 + 76*x^4 + 76*x^3 + 28*x^2 + 121*x + 84, x^73 + 60*x^71 + 112*x^70 + 38*x^69 + 28*x^67 + 112*x^66 + 9*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 38*x^5 + 92*x^3 + 112*x^2 + 113*x + 32, x^73 + 60*x^71 + 44*x^70 + 46*x^69 + 36*x^68 + 76*x^67 + 116*x^66 + 81*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 46*x^5 + 100*x^4 + 12*x^3 + 52*x^2 + 57*x + 124, x^73 + 60*x^71 + 88*x^70 + 102*x^69 + 24*x^68 + 28*x^67 + 72*x^66 + 73*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 102*x^5 + 24*x^4 + 92*x^3 + 72*x^2 + 49*x + 72, x^73 + 60*x^71 + 88*x^70 + 118*x^69 + 104*x^68 + 60*x^67 + 40*x^66 + 25*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 118*x^5 + 104*x^4 + 124*x^3 + 40*x^2 + x + 24, x^73 + 60*x^71 + 4*x^70 + 78*x^69 + 108*x^68 + 12*x^67 + 92*x^66 + 113*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 78*x^5 + 44*x^4 + 76*x^3 + 28*x^2 + 89*x + 116, x^73 + 60*x^71 + 80*x^70 + 118*x^69 + 48*x^68 + 124*x^67 + 48*x^66 + 89*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 118*x^5 + 48*x^4 + 60*x^3 + 48*x^2 + 65*x + 80, x^73 + 60*x^71 + 116*x^70 + 110*x^69 + 28*x^68 + 76*x^67 + 44*x^66 + 17*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 110*x^5 + 92*x^4 + 12*x^3 + 108*x^2 + 121*x + 4, x^73 + 60*x^71 + 56*x^70 + 54*x^69 + 8*x^68 + 124*x^67 + 8*x^66 + 25*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 54*x^5 + 8*x^4 + 60*x^3 + 8*x^2 + x + 56, x^73 + 60*x^71 + 44*x^70 + 110*x^69 + 68*x^68 + 12*x^67 + 116*x^66 + 81*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 110*x^5 + 4*x^4 + 76*x^3 + 52*x^2 + 57*x + 92, x^73 + 60*x^71 + 120*x^70 + 70*x^69 + 24*x^68 + 92*x^67 + 104*x^66 + 41*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 70*x^5 + 24*x^4 + 28*x^3 + 104*x^2 + 17*x + 8, x^73 + 60*x^71 + 88*x^70 + 6*x^69 + 88*x^68 + 92*x^67 + 72*x^66 + 105*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 6*x^5 + 88*x^4 + 28*x^3 + 72*x^2 + 81*x + 8, x^73 + 60*x^71 + 56*x^70 + 86*x^69 + 104*x^68 + 60*x^67 + 72*x^66 + 57*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 86*x^5 + 104*x^4 + 124*x^3 + 72*x^2 + 33*x + 24, x^73 + 60*x^71 + 24*x^70 + 54*x^69 + 104*x^68 + 60*x^67 + 104*x^66 + 89*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 54*x^5 + 104*x^4 + 124*x^3 + 104*x^2 + 65*x + 24, x^73 + 60*x^71 + 36*x^70 + 110*x^69 + 108*x^68 + 76*x^67 + 124*x^66 + 17*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 110*x^5 + 44*x^4 + 12*x^3 + 60*x^2 + 121*x + 52, x^73 + 60*x^71 + 20*x^70 + 126*x^69 + 44*x^68 + 44*x^67 + 108*x^66 + 33*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 126*x^5 + 108*x^4 + 108*x^3 + 44*x^2 + 9*x + 20, x^73 + 60*x^71 + 8*x^70 + 70*x^69 + 40*x^68 + 28*x^67 + 88*x^66 + 105*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 70*x^5 + 40*x^4 + 92*x^3 + 88*x^2 + 81*x + 120, x^73 + 60*x^71 + 56*x^70 + 6*x^69 + 24*x^68 + 28*x^67 + 104*x^66 + 41*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 6*x^5 + 24*x^4 + 92*x^3 + 104*x^2 + 17*x + 72, x^73 + 60*x^71 + 92*x^70 + 46*x^69 + 52*x^68 + 12*x^67 + 4*x^66 + 17*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 46*x^5 + 116*x^4 + 76*x^3 + 68*x^2 + 121*x + 44, x^73 + 60*x^71 + 16*x^70 + 70*x^69 + 96*x^68 + 92*x^67 + 80*x^66 + 41*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 70*x^5 + 96*x^4 + 28*x^3 + 80*x^2 + 17*x + 64, x^73 + 60*x^71 + 108*x^70 + 110*x^69 + 4*x^68 + 12*x^67 + 52*x^66 + 81*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 110*x^5 + 68*x^4 + 76*x^3 + 116*x^2 + 57*x + 28, x^73 + 60*x^71 + 40*x^70 + 6*x^69 + 8*x^68 + 28*x^67 + 56*x^66 + 41*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 6*x^5 + 8*x^4 + 92*x^3 + 56*x^2 + 17*x + 24, x^73 + 60*x^71 + 124*x^70 + 30*x^69 + 68*x^68 + 108*x^67 + 4*x^66 + 65*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 30*x^5 + 4*x^4 + 44*x^3 + 68*x^2 + 41*x + 124, x^73 + 60*x^71 + 72*x^70 + 38*x^69 + 72*x^68 + 28*x^67 + 24*x^66 + 9*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 38*x^5 + 72*x^4 + 92*x^3 + 24*x^2 + 113*x + 88, x^73 + 60*x^71 + 20*x^70 + 78*x^69 + 60*x^68 + 76*x^67 + 76*x^66 + 49*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 78*x^5 + 124*x^4 + 12*x^3 + 12*x^2 + 25*x + 36, x^73 + 60*x^71 + 108*x^70 + 78*x^69 + 100*x^68 + 76*x^67 + 116*x^66 + 49*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 78*x^5 + 36*x^4 + 12*x^3 + 52*x^2 + 25*x + 124, x^73 + 60*x^71 + 108*x^70 + 62*x^69 + 84*x^68 + 44*x^67 + 20*x^66 + 97*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 62*x^5 + 20*x^4 + 108*x^3 + 84*x^2 + 73*x + 108, x^73 + 60*x^71 + 16*x^70 + 102*x^69 + 32*x^68 + 92*x^67 + 16*x^66 + 9*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 102*x^5 + 32*x^4 + 28*x^3 + 16*x^2 + 113*x + 64, x^73 + 60*x^71 + 16*x^70 + 118*x^69 + 48*x^68 + 124*x^67 + 112*x^66 + 89*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 118*x^5 + 48*x^4 + 60*x^3 + 112*x^2 + 65*x + 80, x^73 + 60*x^71 + 120*x^70 + 22*x^69 + 8*x^68 + 60*x^67 + 72*x^66 + 121*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 22*x^5 + 8*x^4 + 124*x^3 + 72*x^2 + 97*x + 56, x^73 + 60*x^71 + 24*x^70 + 6*x^69 + 120*x^68 + 92*x^67 + 72*x^66 + 105*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 6*x^5 + 120*x^4 + 28*x^3 + 72*x^2 + 81*x + 40, x^73 + 60*x^71 + 112*x^70 + 6*x^69 + 32*x^68 + 28*x^67 + 112*x^66 + 41*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 6*x^5 + 32*x^4 + 92*x^3 + 112*x^2 + 17*x, x^73 + 60*x^71 + 16*x^70 + 38*x^69 + 28*x^67 + 16*x^66 + 9*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 38*x^5 + 92*x^3 + 16*x^2 + 113*x + 96, x^73 + 60*x^71 + 108*x^70 + 110*x^69 + 100*x^68 + 12*x^67 + 116*x^66 + 81*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 110*x^5 + 36*x^4 + 76*x^3 + 52*x^2 + 57*x + 124, x^73 + 60*x^71 + 38*x^69 + 80*x^68 + 28*x^67 + 32*x^66 + 9*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 38*x^5 + 80*x^4 + 92*x^3 + 32*x^2 + 113*x + 16, x^73 + 60*x^71 + 68*x^70 + 30*x^69 + 28*x^68 + 44*x^67 + 60*x^66 + x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 30*x^5 + 92*x^4 + 108*x^3 + 124*x^2 + 105*x + 36, x^73 + 60*x^71 + 120*x^70 + 6*x^69 + 120*x^68 + 28*x^67 + 104*x^66 + 41*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 6*x^5 + 120*x^4 + 92*x^3 + 104*x^2 + 17*x + 40, x^73 + 60*x^71 + 84*x^70 + 62*x^69 + 108*x^68 + 44*x^67 + 44*x^66 + 97*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 62*x^5 + 44*x^4 + 108*x^3 + 108*x^2 + 73*x + 84, x^73 + 60*x^71 + 44*x^70 + 126*x^69 + 116*x^68 + 44*x^67 + 20*x^66 + 33*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 126*x^5 + 52*x^4 + 108*x^3 + 84*x^2 + 9*x + 12, x^73 + 60*x^71 + 112*x^70 + 38*x^69 + 64*x^68 + 28*x^67 + 112*x^66 + 9*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 38*x^5 + 64*x^4 + 92*x^3 + 112*x^2 + 113*x + 96, x^73 + 60*x^71 + 8*x^70 + 70*x^69 + 72*x^68 + 92*x^67 + 88*x^66 + 41*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 70*x^5 + 72*x^4 + 28*x^3 + 88*x^2 + 17*x + 88, x^73 + 60*x^71 + 76*x^70 + 30*x^69 + 116*x^68 + 108*x^67 + 52*x^66 + 65*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 30*x^5 + 52*x^4 + 44*x^3 + 116*x^2 + 41*x + 76, x^73 + 60*x^71 + 92*x^70 + 110*x^69 + 52*x^68 + 76*x^67 + 68*x^66 + 17*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 110*x^5 + 116*x^4 + 12*x^3 + 4*x^2 + 121*x + 108, x^73 + 60*x^71 + 36*x^70 + 62*x^69 + 28*x^68 + 44*x^67 + 92*x^66 + 97*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 62*x^5 + 92*x^4 + 108*x^3 + 28*x^2 + 73*x + 36, x^73 + 60*x^71 + 24*x^70 + 38*x^69 + 24*x^68 + 28*x^67 + 8*x^66 + 9*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 38*x^5 + 24*x^4 + 92*x^3 + 8*x^2 + 113*x + 72, x^73 + 60*x^71 + 124*x^70 + 110*x^69 + 84*x^68 + 76*x^67 + 36*x^66 + 17*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 110*x^5 + 20*x^4 + 12*x^3 + 100*x^2 + 121*x + 76, x^73 + 60*x^71 + 96*x^70 + 70*x^69 + 48*x^68 + 92*x^67 + 64*x^66 + 41*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 70*x^5 + 48*x^4 + 28*x^3 + 64*x^2 + 17*x + 48, x^73 + 60*x^71 + 124*x^70 + 94*x^69 + 100*x^68 + 108*x^67 + 68*x^66 + x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 94*x^5 + 36*x^4 + 44*x^3 + 4*x^2 + 105*x + 28, x^73 + 60*x^71 + 86*x^69 + 32*x^68 + 124*x^67 + 121*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 86*x^5 + 32*x^4 + 60*x^3 + 97*x + 96, x^73 + 60*x^71 + 48*x^70 + 118*x^69 + 112*x^68 + 60*x^67 + 80*x^66 + 25*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 118*x^5 + 112*x^4 + 124*x^3 + 80*x^2 + x + 16, x^73 + 60*x^71 + 40*x^70 + 38*x^69 + 8*x^68 + 28*x^67 + 120*x^66 + 9*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 38*x^5 + 8*x^4 + 92*x^3 + 120*x^2 + 113*x + 88, x^73 + 60*x^71 + 24*x^70 + 54*x^69 + 104*x^68 + 124*x^67 + 40*x^66 + 25*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 54*x^5 + 104*x^4 + 60*x^3 + 40*x^2 + x + 88, x^73 + 60*x^71 + 56*x^70 + 38*x^69 + 120*x^68 + 92*x^67 + 40*x^66 + 73*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 38*x^5 + 120*x^4 + 28*x^3 + 40*x^2 + 49*x + 40, x^73 + 60*x^71 + 84*x^70 + 14*x^69 + 92*x^68 + 76*x^67 + 76*x^66 + 113*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 14*x^5 + 28*x^4 + 12*x^3 + 12*x^2 + 89*x + 68, x^73 + 60*x^71 + 68*x^70 + 126*x^69 + 124*x^68 + 108*x^67 + 124*x^66 + 97*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 126*x^5 + 60*x^4 + 44*x^3 + 60*x^2 + 73*x + 4, x^73 + 60*x^71 + 20*x^70 + 46*x^69 + 60*x^68 + 12*x^67 + 76*x^66 + 17*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 46*x^5 + 124*x^4 + 76*x^3 + 12*x^2 + 121*x + 36, x^73 + 60*x^71 + 56*x^70 + 70*x^69 + 120*x^68 + 92*x^67 + 104*x^66 + 41*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 70*x^5 + 120*x^4 + 28*x^3 + 104*x^2 + 17*x + 104, x^73 + 60*x^71 + 108*x^70 + 126*x^69 + 20*x^68 + 108*x^67 + 84*x^66 + 97*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 126*x^5 + 84*x^4 + 44*x^3 + 20*x^2 + 73*x + 108, x^73 + 60*x^71 + 118*x^69 + 96*x^68 + 124*x^67 + 64*x^66 + 89*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 118*x^5 + 96*x^4 + 60*x^3 + 64*x^2 + 65*x + 96, x^73 + 60*x^71 + 120*x^70 + 54*x^69 + 40*x^68 + 60*x^67 + 72*x^66 + 89*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 54*x^5 + 40*x^4 + 124*x^3 + 72*x^2 + 65*x + 24, x^73 + 60*x^71 + 4*x^70 + 14*x^69 + 76*x^68 + 76*x^67 + 92*x^66 + 113*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 14*x^5 + 12*x^4 + 12*x^3 + 28*x^2 + 89*x + 20, x^73 + 60*x^71 + 52*x^70 + 78*x^69 + 92*x^68 + 76*x^67 + 44*x^66 + 49*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 78*x^5 + 28*x^4 + 12*x^3 + 108*x^2 + 25*x + 4, x^73 + 60*x^71 + 112*x^70 + 6*x^69 + 28*x^67 + 48*x^66 + 41*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 6*x^5 + 92*x^3 + 48*x^2 + 17*x + 96, x^73 + 60*x^71 + 124*x^70 + 126*x^69 + 100*x^68 + 44*x^67 + 68*x^66 + 33*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 126*x^5 + 36*x^4 + 108*x^3 + 4*x^2 + 9*x + 28, x^73 + 60*x^71 + 108*x^70 + 78*x^69 + 36*x^68 + 76*x^67 + 116*x^66 + 49*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 78*x^5 + 100*x^4 + 12*x^3 + 52*x^2 + 25*x + 60, x^73 + 60*x^71 + 48*x^70 + 6*x^69 + 92*x^67 + 48*x^66 + 105*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 6*x^5 + 28*x^3 + 48*x^2 + 81*x + 32, x^73 + 60*x^71 + 112*x^70 + 86*x^69 + 80*x^68 + 60*x^67 + 16*x^66 + 57*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 86*x^5 + 80*x^4 + 124*x^3 + 16*x^2 + 33*x + 48, x^73 + 60*x^71 + 104*x^70 + 86*x^69 + 56*x^68 + 60*x^67 + 24*x^66 + 57*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 86*x^5 + 56*x^4 + 124*x^3 + 24*x^2 + 33*x + 72, x^73 + 60*x^71 + 28*x^70 + 62*x^69 + 36*x^68 + 108*x^67 + 36*x^66 + 33*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 62*x^5 + 100*x^4 + 44*x^3 + 100*x^2 + 9*x + 92, x^73 + 60*x^71 + 64*x^70 + 102*x^69 + 16*x^68 + 28*x^67 + 96*x^66 + 73*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 102*x^5 + 16*x^4 + 92*x^3 + 96*x^2 + 49*x + 80, x^73 + 60*x^71 + 36*x^70 + 126*x^69 + 60*x^68 + 44*x^67 + 28*x^66 + 33*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 126*x^5 + 124*x^4 + 108*x^3 + 92*x^2 + 9*x + 68, x^73 + 60*x^71 + 96*x^70 + 102*x^69 + 16*x^68 + 92*x^67 + 64*x^66 + 9*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 102*x^5 + 16*x^4 + 28*x^3 + 64*x^2 + 113*x + 80, x^73 + 60*x^71 + 52*x^70 + 30*x^69 + 44*x^68 + 108*x^67 + 12*x^66 + 65*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 30*x^5 + 108*x^4 + 44*x^3 + 76*x^2 + 41*x + 84, x^73 + 60*x^71 + 104*x^70 + 86*x^69 + 120*x^68 + 60*x^67 + 24*x^66 + 57*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 86*x^5 + 120*x^4 + 124*x^3 + 24*x^2 + 33*x + 8, x^73 + 60*x^71 + 68*x^70 + 78*x^69 + 108*x^68 + 76*x^67 + 92*x^66 + 49*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 78*x^5 + 44*x^4 + 12*x^3 + 28*x^2 + 25*x + 52, x^73 + 60*x^71 + 108*x^70 + 62*x^69 + 52*x^68 + 44*x^67 + 84*x^66 + 97*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 62*x^5 + 116*x^4 + 108*x^3 + 20*x^2 + 73*x + 76, x^73 + 60*x^71 + 4*x^70 + 78*x^69 + 44*x^68 + 12*x^67 + 92*x^66 + 113*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 78*x^5 + 108*x^4 + 76*x^3 + 28*x^2 + 89*x + 52, x^73 + 60*x^71 + 100*x^70 + 14*x^69 + 76*x^68 + 12*x^67 + 124*x^66 + 49*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 14*x^5 + 12*x^4 + 76*x^3 + 60*x^2 + 25*x + 20, x^73 + 60*x^71 + 56*x^70 + 54*x^69 + 104*x^68 + 60*x^67 + 8*x^66 + 89*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 54*x^5 + 104*x^4 + 124*x^3 + 8*x^2 + 65*x + 88, x^73 + 60*x^71 + 44*x^70 + 94*x^69 + 84*x^68 + 108*x^67 + 84*x^66 + x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 94*x^5 + 20*x^4 + 44*x^3 + 20*x^2 + 105*x + 108, x^73 + 60*x^71 + 52*x^70 + 46*x^69 + 60*x^68 + 12*x^67 + 108*x^66 + 17*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 46*x^5 + 124*x^4 + 76*x^3 + 44*x^2 + 121*x + 100, x^73 + 60*x^71 + 120*x^70 + 22*x^69 + 40*x^68 + 124*x^67 + 72*x^66 + 57*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 22*x^5 + 40*x^4 + 60*x^3 + 72*x^2 + 33*x + 24, x^73 + 60*x^71 + 108*x^70 + 110*x^69 + 68*x^68 + 76*x^67 + 116*x^66 + 17*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 110*x^5 + 4*x^4 + 12*x^3 + 52*x^2 + 121*x + 28, x^73 + 60*x^71 + 64*x^70 + 102*x^69 + 112*x^68 + 92*x^67 + 96*x^66 + 9*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 102*x^5 + 112*x^4 + 28*x^3 + 96*x^2 + 113*x + 112, x^73 + 60*x^71 + 96*x^70 + 102*x^69 + 112*x^68 + 28*x^67 + 64*x^66 + 73*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 102*x^5 + 112*x^4 + 92*x^3 + 64*x^2 + 49*x + 112, x^73 + 60*x^71 + 8*x^70 + 6*x^69 + 8*x^68 + 28*x^67 + 24*x^66 + 41*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 6*x^5 + 8*x^4 + 92*x^3 + 24*x^2 + 17*x + 88, x^73 + 60*x^71 + 104*x^70 + 6*x^69 + 8*x^68 + 92*x^67 + 56*x^66 + 105*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 6*x^5 + 8*x^4 + 28*x^3 + 56*x^2 + 81*x + 88, x^73 + 60*x^71 + 12*x^70 + 126*x^69 + 20*x^68 + 44*x^67 + 52*x^66 + 33*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 126*x^5 + 84*x^4 + 108*x^3 + 116*x^2 + 9*x + 108, x^73 + 60*x^71 + 36*x^70 + 94*x^69 + 28*x^68 + 44*x^67 + 28*x^66 + 65*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 94*x^5 + 92*x^4 + 108*x^3 + 92*x^2 + 41*x + 100, x^73 + 60*x^71 + 92*x^70 + 46*x^69 + 84*x^68 + 76*x^67 + 4*x^66 + 81*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 46*x^5 + 20*x^4 + 12*x^3 + 68*x^2 + 57*x + 12, x^73 + 60*x^71 + 124*x^70 + 78*x^69 + 52*x^68 + 12*x^67 + 100*x^66 + 113*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 78*x^5 + 116*x^4 + 76*x^3 + 36*x^2 + 89*x + 44, x^73 + 60*x^71 + 60*x^70 + 126*x^69 + 100*x^68 + 44*x^67 + 4*x^66 + 33*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 126*x^5 + 36*x^4 + 108*x^3 + 68*x^2 + 9*x + 28, x^73 + 60*x^71 + 44*x^70 + 46*x^69 + 68*x^68 + 76*x^67 + 52*x^66 + 81*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 46*x^5 + 4*x^4 + 12*x^3 + 116*x^2 + 57*x + 28, x^73 + 60*x^71 + 84*x^70 + 14*x^69 + 60*x^68 + 76*x^67 + 12*x^66 + 113*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 14*x^5 + 124*x^4 + 12*x^3 + 76*x^2 + 89*x + 36, x^73 + 60*x^71 + 4*x^70 + 30*x^69 + 92*x^68 + 108*x^67 + 60*x^66 + 65*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 30*x^5 + 28*x^4 + 44*x^3 + 124*x^2 + 41*x + 36, x^73 + 60*x^71 + 60*x^70 + 30*x^69 + 68*x^68 + 108*x^67 + 68*x^66 + 65*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 30*x^5 + 4*x^4 + 44*x^3 + 4*x^2 + 41*x + 124, x^73 + 60*x^71 + 108*x^70 + 110*x^69 + 36*x^68 + 76*x^67 + 52*x^66 + 17*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 110*x^5 + 100*x^4 + 12*x^3 + 116*x^2 + 121*x + 124, x^73 + 60*x^71 + 104*x^70 + 38*x^69 + 104*x^68 + 28*x^67 + 120*x^66 + 9*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 38*x^5 + 104*x^4 + 92*x^3 + 120*x^2 + 113*x + 56, x^73 + 60*x^71 + 12*x^70 + 14*x^69 + 68*x^68 + 76*x^67 + 84*x^66 + 113*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 14*x^5 + 4*x^4 + 12*x^3 + 20*x^2 + 89*x + 28, x^73 + 60*x^71 + 68*x^70 + 46*x^69 + 44*x^68 + 12*x^67 + 92*x^66 + 17*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 46*x^5 + 108*x^4 + 76*x^3 + 28*x^2 + 121*x + 116, x^73 + 60*x^71 + 80*x^70 + 54*x^69 + 16*x^68 + 60*x^67 + 48*x^66 + 89*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 54*x^5 + 16*x^4 + 124*x^3 + 48*x^2 + 65*x + 112, x^73 + 60*x^71 + 120*x^70 + 54*x^69 + 8*x^68 + 60*x^67 + 8*x^66 + 89*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 54*x^5 + 8*x^4 + 124*x^3 + 8*x^2 + 65*x + 120, x^73 + 60*x^71 + 64*x^70 + 102*x^69 + 80*x^68 + 28*x^67 + 96*x^66 + 73*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 102*x^5 + 80*x^4 + 92*x^3 + 96*x^2 + 49*x + 16, x^73 + 60*x^71 + 68*x^70 + 14*x^69 + 108*x^68 + 76*x^67 + 92*x^66 + 113*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 14*x^5 + 44*x^4 + 12*x^3 + 28*x^2 + 89*x + 52, x^73 + 60*x^71 + 96*x^70 + 102*x^69 + 80*x^68 + 92*x^67 + 64*x^66 + 9*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 102*x^5 + 80*x^4 + 28*x^3 + 64*x^2 + 113*x + 16, x^73 + 60*x^71 + 8*x^70 + 86*x^69 + 120*x^68 + 60*x^67 + 56*x^66 + 57*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 86*x^5 + 120*x^4 + 124*x^3 + 56*x^2 + 33*x + 72, x^73 + 60*x^71 + 68*x^70 + 94*x^69 + 60*x^68 + 44*x^67 + 124*x^66 + 65*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 94*x^5 + 124*x^4 + 108*x^3 + 60*x^2 + 41*x + 68, x^73 + 60*x^71 + 104*x^70 + 6*x^69 + 104*x^68 + 28*x^67 + 56*x^66 + 41*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 6*x^5 + 104*x^4 + 92*x^3 + 56*x^2 + 17*x + 120, x^73 + 60*x^71 + 88*x^70 + 38*x^69 + 88*x^68 + 28*x^67 + 72*x^66 + 9*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 38*x^5 + 88*x^4 + 92*x^3 + 72*x^2 + 113*x + 8, x^73 + 60*x^71 + 116*x^70 + 126*x^69 + 108*x^68 + 108*x^67 + 12*x^66 + 97*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 126*x^5 + 44*x^4 + 44*x^3 + 76*x^2 + 73*x + 84, x^73 + 60*x^71 + 44*x^70 + 94*x^69 + 116*x^68 + 108*x^67 + 20*x^66 + x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 94*x^5 + 52*x^4 + 44*x^3 + 84*x^2 + 105*x + 12, x^73 + 60*x^71 + 44*x^70 + 14*x^69 + 68*x^68 + 76*x^67 + 116*x^66 + 113*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 14*x^5 + 4*x^4 + 12*x^3 + 52*x^2 + 89*x + 92, x^73 + 60*x^71 + 124*x^70 + 14*x^69 + 20*x^68 + 76*x^67 + 100*x^66 + 113*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 14*x^5 + 84*x^4 + 12*x^3 + 36*x^2 + 89*x + 76, x^73 + 60*x^71 + 108*x^70 + 30*x^69 + 20*x^68 + 108*x^67 + 20*x^66 + 65*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 30*x^5 + 84*x^4 + 44*x^3 + 84*x^2 + 41*x + 44, x^73 + 60*x^71 + 4*x^70 + 62*x^69 + 60*x^68 + 44*x^67 + 124*x^66 + 97*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 62*x^5 + 124*x^4 + 108*x^3 + 60*x^2 + 73*x + 4, x^73 + 60*x^71 + 112*x^70 + 70*x^69 + 64*x^68 + 92*x^67 + 112*x^66 + 41*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 70*x^5 + 64*x^4 + 28*x^3 + 112*x^2 + 17*x + 96, x^73 + 60*x^71 + 56*x^70 + 86*x^69 + 72*x^68 + 124*x^67 + 72*x^66 + 121*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 86*x^5 + 72*x^4 + 60*x^3 + 72*x^2 + 97*x + 56, x^73 + 60*x^71 + 4*x^70 + 46*x^69 + 108*x^68 + 12*x^67 + 28*x^66 + 17*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 46*x^5 + 44*x^4 + 76*x^3 + 92*x^2 + 121*x + 52, x^73 + 60*x^71 + 56*x^70 + 70*x^69 + 88*x^68 + 92*x^67 + 40*x^66 + 41*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 70*x^5 + 88*x^4 + 28*x^3 + 40*x^2 + 17*x + 72, x^73 + 60*x^71 + 24*x^70 + 22*x^69 + 40*x^68 + 124*x^67 + 104*x^66 + 57*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 22*x^5 + 40*x^4 + 60*x^3 + 104*x^2 + 33*x + 88, x^73 + 60*x^71 + 120*x^70 + 102*x^69 + 88*x^68 + 28*x^67 + 104*x^66 + 73*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 102*x^5 + 88*x^4 + 92*x^3 + 104*x^2 + 49*x + 72, x^73 + 60*x^71 + 28*x^70 + 110*x^69 + 84*x^68 + 12*x^67 + 4*x^66 + 81*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 110*x^5 + 20*x^4 + 76*x^3 + 68*x^2 + 57*x + 76, x^73 + 60*x^71 + 112*x^70 + 6*x^69 + 96*x^68 + 92*x^67 + 48*x^66 + 105*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 6*x^5 + 96*x^4 + 28*x^3 + 48*x^2 + 81*x, x^73 + 60*x^71 + 54*x^69 + 96*x^68 + 60*x^67 + 89*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 54*x^5 + 96*x^4 + 124*x^3 + 65*x + 32, x^73 + 60*x^71 + 112*x^70 + 118*x^69 + 112*x^68 + 60*x^67 + 16*x^66 + 25*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 118*x^5 + 112*x^4 + 124*x^3 + 16*x^2 + x + 16, x^73 + 60*x^71 + 4*x^70 + 110*x^69 + 76*x^68 + 12*x^67 + 92*x^66 + 81*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 110*x^5 + 12*x^4 + 76*x^3 + 28*x^2 + 57*x + 20, x^73 + 60*x^71 + 108*x^70 + 46*x^69 + 36*x^68 + 12*x^67 + 116*x^66 + 17*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 46*x^5 + 100*x^4 + 76*x^3 + 52*x^2 + 121*x + 60, x^73 + 60*x^71 + 24*x^70 + 22*x^69 + 104*x^68 + 60*x^67 + 40*x^66 + 121*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 22*x^5 + 104*x^4 + 124*x^3 + 40*x^2 + 97*x + 88, x^73 + 60*x^71 + 116*x^70 + 46*x^69 + 28*x^68 + 12*x^67 + 108*x^66 + 17*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 46*x^5 + 92*x^4 + 76*x^3 + 44*x^2 + 121*x + 68, x^73 + 60*x^71 + 120*x^70 + 22*x^69 + 40*x^68 + 60*x^67 + 8*x^66 + 121*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 22*x^5 + 40*x^4 + 124*x^3 + 8*x^2 + 97*x + 88, x^73 + 60*x^71 + 36*x^70 + 30*x^69 + 124*x^68 + 108*x^67 + 28*x^66 + 65*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 30*x^5 + 60*x^4 + 44*x^3 + 92*x^2 + 41*x + 4, x^73 + 60*x^71 + 16*x^70 + 54*x^69 + 48*x^68 + 124*x^67 + 112*x^66 + 25*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 54*x^5 + 48*x^4 + 60*x^3 + 112*x^2 + x + 80, x^73 + 60*x^71 + 28*x^70 + 110*x^69 + 20*x^68 + 12*x^67 + 4*x^66 + 81*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 110*x^5 + 84*x^4 + 76*x^3 + 68*x^2 + 57*x + 12, x^73 + 60*x^71 + 44*x^70 + 126*x^69 + 20*x^68 + 108*x^67 + 20*x^66 + 97*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 126*x^5 + 84*x^4 + 44*x^3 + 84*x^2 + 73*x + 108, x^73 + 60*x^71 + 86*x^69 + 64*x^68 + 60*x^67 + 57*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 86*x^5 + 64*x^4 + 124*x^3 + 33*x + 64, x^73 + 60*x^71 + 80*x^70 + 70*x^69 + 28*x^67 + 16*x^66 + 105*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 70*x^5 + 92*x^3 + 16*x^2 + 81*x + 32, x^73 + 60*x^71 + 52*x^70 + 94*x^69 + 12*x^68 + 108*x^67 + 76*x^66 + x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 94*x^5 + 76*x^4 + 44*x^3 + 12*x^2 + 105*x + 52, x^73 + 60*x^71 + 88*x^70 + 6*x^69 + 56*x^68 + 28*x^67 + 72*x^66 + 41*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 6*x^5 + 56*x^4 + 92*x^3 + 72*x^2 + 17*x + 40, x^73 + 60*x^71 + 8*x^70 + 102*x^69 + 8*x^68 + 92*x^67 + 24*x^66 + 9*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 102*x^5 + 8*x^4 + 28*x^3 + 24*x^2 + 113*x + 88, x^73 + 60*x^71 + 4*x^70 + 78*x^69 + 76*x^68 + 76*x^67 + 92*x^66 + 49*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 78*x^5 + 12*x^4 + 12*x^3 + 28*x^2 + 25*x + 20, x^73 + 60*x^71 + 68*x^70 + 46*x^69 + 12*x^68 + 12*x^67 + 28*x^66 + 17*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 46*x^5 + 76*x^4 + 76*x^3 + 92*x^2 + 121*x + 84, x^73 + 60*x^71 + 12*x^70 + 14*x^69 + 100*x^68 + 12*x^67 + 84*x^66 + 49*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 14*x^5 + 36*x^4 + 76*x^3 + 20*x^2 + 25*x + 124, x^73 + 60*x^71 + 112*x^70 + 54*x^69 + 16*x^68 + 60*x^67 + 80*x^66 + 89*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 54*x^5 + 16*x^4 + 124*x^3 + 80*x^2 + 65*x + 48, x^73 + 60*x^71 + 52*x^70 + 110*x^69 + 92*x^68 + 12*x^67 + 44*x^66 + 81*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 110*x^5 + 28*x^4 + 76*x^3 + 108*x^2 + 57*x + 4, x^73 + 60*x^71 + 76*x^70 + 14*x^69 + 36*x^68 + 12*x^67 + 20*x^66 + 49*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 14*x^5 + 100*x^4 + 76*x^3 + 84*x^2 + 25*x + 60, x^73 + 60*x^71 + 112*x^70 + 54*x^69 + 80*x^68 + 124*x^67 + 16*x^66 + 25*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 54*x^5 + 80*x^4 + 60*x^3 + 16*x^2 + x + 48, x^73 + 60*x^71 + 92*x^70 + 62*x^69 + 36*x^68 + 44*x^67 + 36*x^66 + 97*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 62*x^5 + 100*x^4 + 108*x^3 + 100*x^2 + 73*x + 28, x^73 + 60*x^71 + 92*x^70 + 14*x^69 + 116*x^68 + 76*x^67 + 4*x^66 + 113*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 14*x^5 + 52*x^4 + 12*x^3 + 68*x^2 + 89*x + 108, x^73 + 60*x^71 + 88*x^70 + 54*x^69 + 8*x^68 + 124*x^67 + 40*x^66 + 25*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 54*x^5 + 8*x^4 + 60*x^3 + 40*x^2 + x + 120, x^73 + 60*x^71 + 92*x^70 + 78*x^69 + 20*x^68 + 76*x^67 + 68*x^66 + 49*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 78*x^5 + 84*x^4 + 12*x^3 + 4*x^2 + 25*x + 12, x^73 + 60*x^71 + 20*x^70 + 126*x^69 + 12*x^68 + 44*x^67 + 44*x^66 + 33*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 126*x^5 + 76*x^4 + 108*x^3 + 108*x^2 + 9*x + 116, x^73 + 60*x^71 + 16*x^70 + 102*x^69 + 64*x^68 + 28*x^67 + 16*x^66 + 73*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 102*x^5 + 64*x^4 + 92*x^3 + 16*x^2 + 49*x + 32, x^73 + 60*x^71 + 40*x^70 + 70*x^69 + 104*x^68 + 92*x^67 + 56*x^66 + 41*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 70*x^5 + 104*x^4 + 28*x^3 + 56*x^2 + 17*x + 56, x^73 + 60*x^71 + 124*x^70 + 14*x^69 + 84*x^68 + 76*x^67 + 100*x^66 + 113*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 14*x^5 + 20*x^4 + 12*x^3 + 36*x^2 + 89*x + 12, x^73 + 60*x^71 + 100*x^70 + 14*x^69 + 44*x^68 + 12*x^67 + 60*x^66 + 49*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 14*x^5 + 108*x^4 + 76*x^3 + 124*x^2 + 25*x + 116, x^73 + 60*x^71 + 92*x^70 + 62*x^69 + 4*x^68 + 108*x^67 + 36*x^66 + 33*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 62*x^5 + 68*x^4 + 44*x^3 + 100*x^2 + 9*x + 60, x^73 + 60*x^71 + 84*x^70 + 94*x^69 + 12*x^68 + 108*x^67 + 108*x^66 + x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 94*x^5 + 76*x^4 + 44*x^3 + 44*x^2 + 105*x + 116, x^73 + 60*x^71 + 104*x^70 + 6*x^69 + 104*x^68 + 92*x^67 + 120*x^66 + 105*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 6*x^5 + 104*x^4 + 28*x^3 + 120*x^2 + 81*x + 56, x^73 + 60*x^71 + 124*x^70 + 110*x^69 + 52*x^68 + 76*x^67 + 100*x^66 + 17*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 110*x^5 + 116*x^4 + 12*x^3 + 36*x^2 + 121*x + 44, x^73 + 60*x^71 + 52*x^70 + 62*x^69 + 108*x^68 + 108*x^67 + 76*x^66 + 33*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 62*x^5 + 44*x^4 + 44*x^3 + 12*x^2 + 9*x + 84, x^73 + 60*x^71 + 48*x^70 + 118*x^69 + 48*x^68 + 124*x^67 + 16*x^66 + 89*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 118*x^5 + 48*x^4 + 60*x^3 + 16*x^2 + 65*x + 16, x^73 + 60*x^71 + 112*x^70 + 22*x^69 + 80*x^68 + 124*x^67 + 80*x^66 + 57*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 22*x^5 + 80*x^4 + 60*x^3 + 80*x^2 + 33*x + 112, x^73 + 60*x^71 + 92*x^70 + 14*x^69 + 84*x^68 + 12*x^67 + 4*x^66 + 49*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 14*x^5 + 20*x^4 + 76*x^3 + 68*x^2 + 25*x + 12, x^73 + 60*x^71 + 56*x^70 + 102*x^69 + 56*x^68 + 28*x^67 + 104*x^66 + 73*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 102*x^5 + 56*x^4 + 92*x^3 + 104*x^2 + 49*x + 40, x^73 + 60*x^71 + 108*x^70 + 110*x^69 + 68*x^68 + 12*x^67 + 52*x^66 + 81*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 110*x^5 + 4*x^4 + 76*x^3 + 116*x^2 + 57*x + 92, x^73 + 60*x^71 + 56*x^70 + 22*x^69 + 8*x^68 + 60*x^67 + 8*x^66 + 121*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 22*x^5 + 8*x^4 + 124*x^3 + 8*x^2 + 97*x + 56, x^73 + 60*x^71 + 20*x^70 + 14*x^69 + 28*x^68 + 12*x^67 + 76*x^66 + 49*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 14*x^5 + 92*x^4 + 76*x^3 + 12*x^2 + 25*x + 68, x^73 + 60*x^71 + 4*x^70 + 110*x^69 + 12*x^68 + 76*x^67 + 28*x^66 + 17*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 110*x^5 + 76*x^4 + 12*x^3 + 92*x^2 + 121*x + 20, x^73 + 60*x^71 + 64*x^70 + 86*x^69 + 64*x^68 + 60*x^67 + 64*x^66 + 57*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 86*x^5 + 64*x^4 + 124*x^3 + 64*x^2 + 33*x + 64, x^73 + 60*x^71 + 28*x^70 + 78*x^69 + 52*x^68 + 76*x^67 + 68*x^66 + 49*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 78*x^5 + 116*x^4 + 12*x^3 + 4*x^2 + 25*x + 44, x^73 + 60*x^71 + 80*x^70 + 102*x^69 + 32*x^68 + 92*x^67 + 80*x^66 + 9*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 102*x^5 + 32*x^4 + 28*x^3 + 80*x^2 + 113*x + 64, x^73 + 60*x^71 + 116*x^70 + 14*x^69 + 92*x^68 + 12*x^67 + 44*x^66 + 49*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 14*x^5 + 28*x^4 + 76*x^3 + 108*x^2 + 25*x + 68, x^73 + 60*x^71 + 84*x^70 + 126*x^69 + 108*x^68 + 108*x^67 + 108*x^66 + 97*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 126*x^5 + 44*x^4 + 44*x^3 + 44*x^2 + 73*x + 20, x^73 + 60*x^71 + 24*x^70 + 54*x^69 + 40*x^68 + 124*x^67 + 40*x^66 + 25*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 54*x^5 + 40*x^4 + 60*x^3 + 40*x^2 + x + 24, x^73 + 60*x^71 + 56*x^70 + 38*x^69 + 24*x^68 + 92*x^67 + 104*x^66 + 73*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 38*x^5 + 24*x^4 + 28*x^3 + 104*x^2 + 49*x + 72, x^73 + 60*x^71 + 40*x^70 + 70*x^69 + 8*x^68 + 28*x^67 + 56*x^66 + 105*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 70*x^5 + 8*x^4 + 92*x^3 + 56*x^2 + 81*x + 24, x^73 + 60*x^71 + 48*x^70 + 70*x^69 + 32*x^68 + 28*x^67 + 48*x^66 + 105*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 70*x^5 + 32*x^4 + 92*x^3 + 48*x^2 + 81*x, x^73 + 60*x^71 + 112*x^70 + 118*x^69 + 80*x^68 + 60*x^67 + 80*x^66 + 25*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 118*x^5 + 80*x^4 + 124*x^3 + 80*x^2 + x + 112, x^73 + 60*x^71 + 16*x^70 + 86*x^69 + 112*x^68 + 124*x^67 + 48*x^66 + 121*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 86*x^5 + 112*x^4 + 60*x^3 + 48*x^2 + 97*x + 80, x^73 + 60*x^71 + 100*x^70 + 126*x^69 + 92*x^68 + 44*x^67 + 28*x^66 + 33*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 126*x^5 + 28*x^4 + 108*x^3 + 92*x^2 + 9*x + 100, x^73 + 60*x^71 + 112*x^70 + 38*x^69 + 92*x^67 + 48*x^66 + 73*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 38*x^5 + 28*x^3 + 48*x^2 + 49*x + 96, x^73 + 60*x^71 + 16*x^70 + 54*x^69 + 16*x^68 + 60*x^67 + 112*x^66 + 89*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 54*x^5 + 16*x^4 + 124*x^3 + 112*x^2 + 65*x + 112, x^73 + 60*x^71 + 28*x^70 + 126*x^69 + 4*x^68 + 108*x^67 + 100*x^66 + 97*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 126*x^5 + 68*x^4 + 44*x^3 + 36*x^2 + 73*x + 60, x^73 + 60*x^71 + 120*x^70 + 86*x^69 + 8*x^68 + 60*x^67 + 72*x^66 + 57*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 86*x^5 + 8*x^4 + 124*x^3 + 72*x^2 + 33*x + 56, x^73 + 60*x^71 + 96*x^70 + 86*x^69 + 60*x^67 + 96*x^66 + 57*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 86*x^5 + 124*x^3 + 96*x^2 + 33*x + 64, x^73 + 60*x^71 + 68*x^70 + 30*x^69 + 92*x^68 + 108*x^67 + 124*x^66 + 65*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 30*x^5 + 28*x^4 + 44*x^3 + 60*x^2 + 41*x + 36, x^73 + 60*x^71 + 124*x^70 + 62*x^69 + 4*x^68 + 108*x^67 + 68*x^66 + 33*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 62*x^5 + 68*x^4 + 44*x^3 + 4*x^2 + 9*x + 124, x^73 + 60*x^71 + 4*x^70 + 14*x^69 + 12*x^68 + 76*x^67 + 92*x^66 + 113*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 14*x^5 + 76*x^4 + 12*x^3 + 28*x^2 + 89*x + 84, x^73 + 60*x^71 + 92*x^70 + 14*x^69 + 20*x^68 + 12*x^67 + 4*x^66 + 49*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 14*x^5 + 84*x^4 + 76*x^3 + 68*x^2 + 25*x + 76, x^73 + 60*x^71 + 92*x^70 + 46*x^69 + 20*x^68 + 12*x^67 + 68*x^66 + 17*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 46*x^5 + 84*x^4 + 76*x^3 + 4*x^2 + 121*x + 12, x^73 + 60*x^71 + 96*x^70 + 118*x^69 + 60*x^67 + 32*x^66 + 25*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 118*x^5 + 124*x^3 + 32*x^2 + x, x^73 + 60*x^71 + 52*x^70 + 94*x^69 + 108*x^68 + 44*x^67 + 76*x^66 + 65*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 94*x^5 + 44*x^4 + 108*x^3 + 12*x^2 + 41*x + 84, x^73 + 60*x^71 + 102*x^69 + 48*x^68 + 28*x^67 + 96*x^66 + 73*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 102*x^5 + 48*x^4 + 92*x^3 + 96*x^2 + 49*x + 112, x^73 + 60*x^71 + 112*x^70 + 38*x^69 + 64*x^68 + 92*x^67 + 48*x^66 + 73*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 38*x^5 + 64*x^4 + 28*x^3 + 48*x^2 + 49*x + 32, x^73 + 60*x^71 + 56*x^70 + 38*x^69 + 24*x^68 + 28*x^67 + 40*x^66 + 9*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 38*x^5 + 24*x^4 + 92*x^3 + 40*x^2 + 113*x + 8, x^73 + 60*x^71 + 40*x^70 + 102*x^69 + 40*x^68 + 92*x^67 + 120*x^66 + 9*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 102*x^5 + 40*x^4 + 28*x^3 + 120*x^2 + 113*x + 56, x^73 + 60*x^71 + 12*x^70 + 126*x^69 + 116*x^68 + 108*x^67 + 52*x^66 + 97*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 126*x^5 + 52*x^4 + 44*x^3 + 116*x^2 + 73*x + 12, x^73 + 60*x^71 + 96*x^70 + 102*x^69 + 48*x^68 + 92*x^67 + 9*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 102*x^5 + 48*x^4 + 28*x^3 + 113*x + 112, x^73 + 60*x^71 + 32*x^70 + 86*x^69 + 64*x^68 + 60*x^67 + 32*x^66 + 57*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 86*x^5 + 64*x^4 + 124*x^3 + 32*x^2 + 33*x, x^73 + 60*x^71 + 80*x^70 + 86*x^69 + 112*x^68 + 60*x^67 + 48*x^66 + 57*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 86*x^5 + 112*x^4 + 124*x^3 + 48*x^2 + 33*x + 16, x^73 + 60*x^71 + 60*x^70 + 30*x^69 + 100*x^68 + 108*x^67 + 4*x^66 + 65*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 30*x^5 + 36*x^4 + 44*x^3 + 68*x^2 + 41*x + 28, x^73 + 60*x^71 + 120*x^70 + 38*x^69 + 56*x^68 + 28*x^67 + 40*x^66 + 9*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 38*x^5 + 56*x^4 + 92*x^3 + 40*x^2 + 113*x + 40, x^73 + 60*x^71 + 40*x^70 + 38*x^69 + 72*x^68 + 92*x^67 + 56*x^66 + 73*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 38*x^5 + 72*x^4 + 28*x^3 + 56*x^2 + 49*x + 88, x^73 + 60*x^71 + 56*x^70 + 54*x^69 + 40*x^68 + 60*x^67 + 8*x^66 + 89*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 54*x^5 + 40*x^4 + 124*x^3 + 8*x^2 + 65*x + 24, x^73 + 60*x^71 + 92*x^70 + 94*x^69 + 68*x^68 + 108*x^67 + 100*x^66 + x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 94*x^5 + 4*x^4 + 44*x^3 + 36*x^2 + 105*x + 60, x^73 + 60*x^71 + 88*x^70 + 86*x^69 + 8*x^68 + 124*x^67 + 104*x^66 + 121*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 86*x^5 + 8*x^4 + 60*x^3 + 104*x^2 + 97*x + 56, x^73 + 60*x^71 + 88*x^70 + 86*x^69 + 104*x^68 + 60*x^67 + 104*x^66 + 57*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 86*x^5 + 104*x^4 + 124*x^3 + 104*x^2 + 33*x + 88, x^73 + 60*x^71 + 100*x^70 + 30*x^69 + 60*x^68 + 108*x^67 + 92*x^66 + 65*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 30*x^5 + 124*x^4 + 44*x^3 + 28*x^2 + 41*x + 68, x^73 + 60*x^71 + 12*x^70 + 94*x^69 + 20*x^68 + 108*x^67 + 52*x^66 + x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 94*x^5 + 84*x^4 + 44*x^3 + 116*x^2 + 105*x + 108, x^73 + 60*x^71 + 112*x^70 + 38*x^69 + 96*x^68 + 92*x^67 + 112*x^66 + 73*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 38*x^5 + 96*x^4 + 28*x^3 + 112*x^2 + 49*x + 64, x^73 + 60*x^71 + 96*x^70 + 54*x^69 + 32*x^68 + 124*x^67 + 32*x^66 + 25*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 54*x^5 + 32*x^4 + 60*x^3 + 32*x^2 + x + 96, x^73 + 60*x^71 + 12*x^70 + 126*x^69 + 52*x^68 + 44*x^67 + 116*x^66 + 33*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 126*x^5 + 116*x^4 + 108*x^3 + 52*x^2 + 9*x + 12, x^73 + 60*x^71 + 16*x^70 + 118*x^69 + 112*x^68 + 60*x^67 + 48*x^66 + 25*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 118*x^5 + 112*x^4 + 124*x^3 + 48*x^2 + x + 80, x^73 + 60*x^71 + 84*x^70 + 62*x^69 + 44*x^68 + 44*x^67 + 44*x^66 + 97*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 62*x^5 + 108*x^4 + 108*x^3 + 108*x^2 + 73*x + 20, x^73 + 60*x^71 + 104*x^70 + 54*x^69 + 24*x^68 + 124*x^67 + 88*x^66 + 25*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 54*x^5 + 24*x^4 + 60*x^3 + 88*x^2 + x + 40, x^73 + 60*x^71 + 16*x^70 + 86*x^69 + 80*x^68 + 60*x^67 + 48*x^66 + 57*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 86*x^5 + 80*x^4 + 124*x^3 + 48*x^2 + 33*x + 112, x^73 + 60*x^71 + 44*x^70 + 14*x^69 + 100*x^68 + 76*x^67 + 52*x^66 + 113*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 14*x^5 + 36*x^4 + 12*x^3 + 116*x^2 + 89*x + 124, x^73 + 60*x^71 + 68*x^70 + 94*x^69 + 92*x^68 + 44*x^67 + 60*x^66 + 65*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 94*x^5 + 28*x^4 + 108*x^3 + 124*x^2 + 41*x + 100, x^73 + 60*x^71 + 48*x^70 + 118*x^69 + 16*x^68 + 124*x^67 + 80*x^66 + 89*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 118*x^5 + 16*x^4 + 60*x^3 + 80*x^2 + 65*x + 112, x^73 + 60*x^71 + 100*x^70 + 94*x^69 + 124*x^68 + 108*x^67 + 92*x^66 + x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 94*x^5 + 60*x^4 + 44*x^3 + 28*x^2 + 105*x + 4, x^73 + 60*x^71 + 36*x^70 + 46*x^69 + 44*x^68 + 76*x^67 + 124*x^66 + 81*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 46*x^5 + 108*x^4 + 12*x^3 + 60*x^2 + 57*x + 116, x^73 + 60*x^71 + 24*x^70 + 102*x^69 + 120*x^68 + 28*x^67 + 72*x^66 + 73*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 102*x^5 + 120*x^4 + 92*x^3 + 72*x^2 + 49*x + 40, x^73 + 60*x^71 + 44*x^70 + 46*x^69 + 68*x^68 + 12*x^67 + 116*x^66 + 17*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 46*x^5 + 4*x^4 + 76*x^3 + 52*x^2 + 121*x + 92, x^73 + 60*x^71 + 56*x^70 + 22*x^69 + 72*x^68 + 60*x^67 + 8*x^66 + 121*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 22*x^5 + 72*x^4 + 124*x^3 + 8*x^2 + 97*x + 120, x^73 + 60*x^71 + 116*x^70 + 94*x^69 + 76*x^68 + 108*x^67 + 12*x^66 + x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 94*x^5 + 12*x^4 + 44*x^3 + 76*x^2 + 105*x + 116, x^73 + 60*x^71 + 112*x^70 + 102*x^69 + 64*x^68 + 92*x^67 + 48*x^66 + 9*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 102*x^5 + 64*x^4 + 28*x^3 + 48*x^2 + 113*x + 32, x^73 + 60*x^71 + 108*x^70 + 126*x^69 + 52*x^68 + 108*x^67 + 20*x^66 + 97*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 126*x^5 + 116*x^4 + 44*x^3 + 84*x^2 + 73*x + 12, x^73 + 60*x^71 + 102*x^69 + 112*x^68 + 28*x^67 + 96*x^66 + 73*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 102*x^5 + 112*x^4 + 92*x^3 + 96*x^2 + 49*x + 48, x^73 + 60*x^71 + 36*x^70 + 14*x^69 + 44*x^68 + 12*x^67 + 124*x^66 + 49*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 14*x^5 + 108*x^4 + 76*x^3 + 60*x^2 + 25*x + 116, x^73 + 60*x^71 + 4*x^70 + 30*x^69 + 92*x^68 + 44*x^67 + 124*x^66 + x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 30*x^5 + 28*x^4 + 108*x^3 + 60*x^2 + 105*x + 100, x^73 + 60*x^71 + 44*x^70 + 126*x^69 + 20*x^68 + 44*x^67 + 84*x^66 + 33*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 126*x^5 + 84*x^4 + 108*x^3 + 20*x^2 + 9*x + 44, x^73 + 60*x^71 + 96*x^70 + 102*x^69 + 112*x^68 + 92*x^67 + 9*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 102*x^5 + 112*x^4 + 28*x^3 + 113*x + 48, x^73 + 60*x^71 + 16*x^70 + 22*x^69 + 16*x^68 + 60*x^67 + 48*x^66 + 121*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 22*x^5 + 16*x^4 + 124*x^3 + 48*x^2 + 97*x + 48, x^73 + 60*x^71 + 112*x^70 + 54*x^69 + 48*x^68 + 60*x^67 + 16*x^66 + 89*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 54*x^5 + 48*x^4 + 124*x^3 + 16*x^2 + 65*x + 80, x^73 + 60*x^71 + 56*x^70 + 86*x^69 + 40*x^68 + 124*x^67 + 8*x^66 + 121*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 86*x^5 + 40*x^4 + 60*x^3 + 8*x^2 + 97*x + 24, x^73 + 60*x^71 + 64*x^70 + 118*x^69 + 96*x^68 + 124*x^67 + 89*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 118*x^5 + 96*x^4 + 60*x^3 + 65*x + 96, x^73 + 60*x^71 + 92*x^70 + 78*x^69 + 52*x^68 + 76*x^67 + 4*x^66 + 49*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 78*x^5 + 116*x^4 + 12*x^3 + 68*x^2 + 25*x + 44, x^73 + 60*x^71 + 120*x^70 + 70*x^69 + 120*x^68 + 92*x^67 + 40*x^66 + 41*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 70*x^5 + 120*x^4 + 28*x^3 + 40*x^2 + 17*x + 104, x^73 + 60*x^71 + 124*x^70 + 110*x^69 + 116*x^68 + 76*x^67 + 100*x^66 + 17*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 110*x^5 + 52*x^4 + 12*x^3 + 36*x^2 + 121*x + 108, x^73 + 60*x^71 + 112*x^70 + 22*x^69 + 112*x^68 + 124*x^67 + 16*x^66 + 57*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 22*x^5 + 112*x^4 + 60*x^3 + 16*x^2 + 33*x + 16, x^73 + 60*x^71 + 8*x^70 + 70*x^69 + 8*x^68 + 28*x^67 + 24*x^66 + 105*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 70*x^5 + 8*x^4 + 92*x^3 + 24*x^2 + 81*x + 88, x^73 + 60*x^71 + 80*x^70 + 86*x^69 + 80*x^68 + 60*x^67 + 112*x^66 + 57*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 86*x^5 + 80*x^4 + 124*x^3 + 112*x^2 + 33*x + 112, x^73 + 60*x^71 + 92*x^70 + 94*x^69 + 100*x^68 + 108*x^67 + 36*x^66 + x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 94*x^5 + 36*x^4 + 44*x^3 + 100*x^2 + 105*x + 92, x^73 + 60*x^71 + 24*x^70 + 54*x^69 + 72*x^68 + 124*x^67 + 104*x^66 + 25*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 54*x^5 + 72*x^4 + 60*x^3 + 104*x^2 + x + 56, x^73 + 60*x^71 + 52*x^70 + 14*x^69 + 92*x^68 + 76*x^67 + 44*x^66 + 113*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 14*x^5 + 28*x^4 + 12*x^3 + 108*x^2 + 89*x + 4, x^73 + 60*x^71 + 16*x^70 + 70*x^69 + 96*x^68 + 28*x^67 + 16*x^66 + 105*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 70*x^5 + 96*x^4 + 92*x^3 + 16*x^2 + 81*x, x^73 + 60*x^71 + 84*x^70 + 30*x^69 + 108*x^68 + 44*x^67 + 108*x^66 + x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 30*x^5 + 44*x^4 + 108*x^3 + 44*x^2 + 105*x + 20, x^73 + 60*x^71 + 44*x^70 + 62*x^69 + 116*x^68 + 44*x^67 + 20*x^66 + 97*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 62*x^5 + 52*x^4 + 108*x^3 + 84*x^2 + 73*x + 12, x^73 + 60*x^71 + 96*x^70 + 86*x^69 + 124*x^67 + 32*x^66 + 121*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 86*x^5 + 60*x^3 + 32*x^2 + 97*x, x^73 + 60*x^71 + 84*x^70 + 94*x^69 + 76*x^68 + 108*x^67 + 108*x^66 + x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 94*x^5 + 12*x^4 + 44*x^3 + 44*x^2 + 105*x + 52, x^73 + 60*x^71 + 12*x^70 + 30*x^69 + 52*x^68 + 108*x^67 + 116*x^66 + 65*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 30*x^5 + 116*x^4 + 44*x^3 + 52*x^2 + 41*x + 12, x^73 + 60*x^71 + 16*x^70 + 86*x^69 + 112*x^68 + 60*x^67 + 112*x^66 + 57*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 86*x^5 + 112*x^4 + 124*x^3 + 112*x^2 + 33*x + 16, x^73 + 60*x^71 + 32*x^70 + 6*x^69 + 48*x^68 + 28*x^67 + 64*x^66 + 41*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 6*x^5 + 48*x^4 + 92*x^3 + 64*x^2 + 17*x + 112, x^73 + 60*x^71 + 40*x^70 + 102*x^69 + 8*x^68 + 92*x^67 + 56*x^66 + 9*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 102*x^5 + 8*x^4 + 28*x^3 + 56*x^2 + 113*x + 24, x^73 + 60*x^71 + 100*x^70 + 126*x^69 + 124*x^68 + 108*x^67 + 28*x^66 + 97*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 126*x^5 + 60*x^4 + 44*x^3 + 92*x^2 + 73*x + 68, x^73 + 60*x^71 + 60*x^70 + 14*x^69 + 116*x^68 + 12*x^67 + 36*x^66 + 49*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 14*x^5 + 52*x^4 + 76*x^3 + 100*x^2 + 25*x + 108, x^73 + 60*x^71 + 102*x^69 + 16*x^68 + 92*x^67 + 96*x^66 + 9*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 102*x^5 + 16*x^4 + 28*x^3 + 96*x^2 + 113*x + 16, x^73 + 60*x^71 + 24*x^70 + 6*x^69 + 56*x^68 + 92*x^67 + 72*x^66 + 105*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 6*x^5 + 56*x^4 + 28*x^3 + 72*x^2 + 81*x + 104, x^73 + 60*x^71 + 80*x^70 + 6*x^69 + 32*x^68 + 92*x^67 + 16*x^66 + 105*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 6*x^5 + 32*x^4 + 28*x^3 + 16*x^2 + 81*x, x^73 + 60*x^71 + 12*x^70 + 46*x^69 + 36*x^68 + 76*x^67 + 84*x^66 + 81*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 46*x^5 + 100*x^4 + 12*x^3 + 20*x^2 + 57*x + 60, x^73 + 60*x^71 + 96*x^70 + 102*x^69 + 16*x^68 + 28*x^67 + 73*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 102*x^5 + 16*x^4 + 92*x^3 + 49*x + 16, x^73 + 60*x^71 + 12*x^70 + 14*x^69 + 36*x^68 + 12*x^67 + 84*x^66 + 49*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 14*x^5 + 100*x^4 + 76*x^3 + 20*x^2 + 25*x + 60, x^73 + 60*x^71 + 112*x^70 + 118*x^69 + 16*x^68 + 124*x^67 + 16*x^66 + 89*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 118*x^5 + 16*x^4 + 60*x^3 + 16*x^2 + 65*x + 112, x^73 + 60*x^71 + 76*x^70 + 94*x^69 + 116*x^68 + 108*x^67 + 52*x^66 + x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 94*x^5 + 52*x^4 + 44*x^3 + 116*x^2 + 105*x + 76, x^73 + 60*x^71 + 112*x^70 + 102*x^69 + 96*x^68 + 28*x^67 + 48*x^66 + 73*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 102*x^5 + 96*x^4 + 92*x^3 + 48*x^2 + 49*x, x^73 + 60*x^71 + 120*x^70 + 118*x^69 + 8*x^68 + 60*x^67 + 8*x^66 + 25*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 118*x^5 + 8*x^4 + 124*x^3 + 8*x^2 + x + 120, x^73 + 60*x^71 + 80*x^70 + 118*x^69 + 112*x^68 + 124*x^67 + 48*x^66 + 89*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 118*x^5 + 112*x^4 + 60*x^3 + 48*x^2 + 65*x + 16, x^73 + 60*x^71 + 116*x^70 + 62*x^69 + 76*x^68 + 44*x^67 + 12*x^66 + 97*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 62*x^5 + 12*x^4 + 108*x^3 + 76*x^2 + 73*x + 116, x^73 + 60*x^71 + 80*x^70 + 102*x^69 + 64*x^68 + 28*x^67 + 80*x^66 + 73*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 102*x^5 + 64*x^4 + 92*x^3 + 80*x^2 + 49*x + 32, x^73 + 60*x^71 + 88*x^70 + 118*x^69 + 40*x^68 + 124*x^67 + 104*x^66 + 89*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 118*x^5 + 40*x^4 + 60*x^3 + 104*x^2 + 65*x + 24, x^73 + 60*x^71 + 88*x^70 + 6*x^69 + 24*x^68 + 92*x^67 + 72*x^66 + 105*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 6*x^5 + 24*x^4 + 28*x^3 + 72*x^2 + 81*x + 72, x^73 + 60*x^71 + 60*x^70 + 14*x^69 + 52*x^68 + 12*x^67 + 36*x^66 + 49*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 14*x^5 + 116*x^4 + 76*x^3 + 100*x^2 + 25*x + 44, x^73 + 60*x^71 + 28*x^70 + 14*x^69 + 84*x^68 + 12*x^67 + 68*x^66 + 49*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 14*x^5 + 20*x^4 + 76*x^3 + 4*x^2 + 25*x + 12, x^73 + 60*x^71 + 86*x^69 + 96*x^68 + 124*x^67 + 121*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 86*x^5 + 96*x^4 + 60*x^3 + 97*x + 32, x^73 + 60*x^71 + 28*x^70 + 62*x^69 + 36*x^68 + 44*x^67 + 100*x^66 + 97*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 62*x^5 + 100*x^4 + 108*x^3 + 36*x^2 + 73*x + 28, x^73 + 60*x^71 + 32*x^70 + 6*x^69 + 112*x^68 + 28*x^67 + 64*x^66 + 41*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 6*x^5 + 112*x^4 + 92*x^3 + 64*x^2 + 17*x + 48, x^73 + 60*x^71 + 44*x^70 + 14*x^69 + 68*x^68 + 12*x^67 + 52*x^66 + 49*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 14*x^5 + 4*x^4 + 76*x^3 + 116*x^2 + 25*x + 28, x^73 + 60*x^71 + 120*x^70 + 54*x^69 + 104*x^68 + 124*x^67 + 8*x^66 + 25*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 54*x^5 + 104*x^4 + 60*x^3 + 8*x^2 + x + 24, x^73 + 60*x^71 + 120*x^70 + 22*x^69 + 72*x^68 + 60*x^67 + 72*x^66 + 121*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 22*x^5 + 72*x^4 + 124*x^3 + 72*x^2 + 97*x + 120, x^73 + 60*x^71 + 116*x^70 + 46*x^69 + 28*x^68 + 76*x^67 + 44*x^66 + 81*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 46*x^5 + 92*x^4 + 12*x^3 + 108*x^2 + 57*x + 4, x^73 + 60*x^71 + 44*x^70 + 62*x^69 + 84*x^68 + 108*x^67 + 20*x^66 + 33*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 62*x^5 + 20*x^4 + 44*x^3 + 84*x^2 + 9*x + 44, x^73 + 60*x^71 + 118*x^69 + 64*x^68 + 124*x^67 + 89*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 118*x^5 + 64*x^4 + 60*x^3 + 65*x + 64, x^73 + 60*x^71 + 72*x^70 + 118*x^69 + 120*x^68 + 124*x^67 + 120*x^66 + 89*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 118*x^5 + 120*x^4 + 60*x^3 + 120*x^2 + 65*x + 72, x^73 + 60*x^71 + 60*x^70 + 126*x^69 + 4*x^68 + 44*x^67 + 68*x^66 + 33*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 126*x^5 + 68*x^4 + 108*x^3 + 4*x^2 + 9*x + 60, x^73 + 60*x^71 + 44*x^70 + 46*x^69 + 100*x^68 + 12*x^67 + 52*x^66 + 17*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 46*x^5 + 36*x^4 + 76*x^3 + 116*x^2 + 121*x + 124, x^73 + 60*x^71 + 40*x^70 + 118*x^69 + 24*x^68 + 124*x^67 + 24*x^66 + 89*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 118*x^5 + 24*x^4 + 60*x^3 + 24*x^2 + 65*x + 40, x^73 + 60*x^71 + 16*x^70 + 6*x^69 + 96*x^68 + 28*x^67 + 16*x^66 + 41*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 6*x^5 + 96*x^4 + 92*x^3 + 16*x^2 + 17*x, x^73 + 60*x^71 + 48*x^70 + 54*x^69 + 80*x^68 + 60*x^67 + 16*x^66 + 89*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 54*x^5 + 80*x^4 + 124*x^3 + 16*x^2 + 65*x + 112, x^73 + 60*x^71 + 44*x^70 + 14*x^69 + 4*x^68 + 12*x^67 + 52*x^66 + 49*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 14*x^5 + 68*x^4 + 76*x^3 + 116*x^2 + 25*x + 92, x^73 + 60*x^71 + 48*x^70 + 102*x^69 + 28*x^67 + 48*x^66 + 73*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 102*x^5 + 92*x^3 + 48*x^2 + 49*x + 32, x^73 + 60*x^71 + 112*x^70 + 86*x^69 + 16*x^68 + 124*x^67 + 80*x^66 + 121*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 86*x^5 + 16*x^4 + 60*x^3 + 80*x^2 + 97*x + 48, x^73 + 60*x^71 + 68*x^70 + 62*x^69 + 28*x^68 + 108*x^67 + 60*x^66 + 33*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 62*x^5 + 92*x^4 + 44*x^3 + 124*x^2 + 9*x + 36, x^73 + 60*x^71 + 16*x^70 + 86*x^69 + 80*x^68 + 124*x^67 + 112*x^66 + 121*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 86*x^5 + 80*x^4 + 60*x^3 + 112*x^2 + 97*x + 48, x^73 + 60*x^71 + 56*x^70 + 86*x^69 + 8*x^68 + 60*x^67 + 8*x^66 + 57*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 86*x^5 + 8*x^4 + 124*x^3 + 8*x^2 + 33*x + 56, x^73 + 60*x^71 + 116*x^70 + 62*x^69 + 12*x^68 + 44*x^67 + 12*x^66 + 97*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 62*x^5 + 76*x^4 + 108*x^3 + 76*x^2 + 73*x + 52, x^73 + 60*x^71 + 72*x^70 + 86*x^69 + 88*x^68 + 124*x^67 + 120*x^66 + 121*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 86*x^5 + 88*x^4 + 60*x^3 + 120*x^2 + 97*x + 104, x^73 + 60*x^71 + 32*x^70 + 22*x^69 + 124*x^67 + 96*x^66 + 57*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 22*x^5 + 60*x^3 + 96*x^2 + 33*x, x^73 + 60*x^71 + 12*x^70 + 94*x^69 + 116*x^68 + 108*x^67 + 116*x^66 + x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 94*x^5 + 52*x^4 + 44*x^3 + 52*x^2 + 105*x + 76, x^73 + 60*x^71 + 44*x^70 + 62*x^69 + 84*x^68 + 44*x^67 + 84*x^66 + 97*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 62*x^5 + 20*x^4 + 108*x^3 + 20*x^2 + 73*x + 108, x^73 + 60*x^71 + 20*x^70 + 94*x^69 + 76*x^68 + 108*x^67 + 44*x^66 + x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 94*x^5 + 12*x^4 + 44*x^3 + 108*x^2 + 105*x + 52, x^73 + 60*x^71 + 108*x^70 + 30*x^69 + 116*x^68 + 44*x^67 + 20*x^66 + x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 30*x^5 + 52*x^4 + 108*x^3 + 84*x^2 + 105*x + 76, x^73 + 60*x^71 + 124*x^70 + 30*x^69 + 100*x^68 + 108*x^67 + 68*x^66 + 65*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 30*x^5 + 36*x^4 + 44*x^3 + 4*x^2 + 41*x + 28, x^73 + 60*x^71 + 60*x^70 + 126*x^69 + 36*x^68 + 108*x^67 + 68*x^66 + 97*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 126*x^5 + 100*x^4 + 44*x^3 + 4*x^2 + 73*x + 28, x^73 + 60*x^71 + 8*x^70 + 70*x^69 + 40*x^68 + 92*x^67 + 24*x^66 + 41*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 70*x^5 + 40*x^4 + 28*x^3 + 24*x^2 + 17*x + 56, x^73 + 60*x^71 + 96*x^70 + 38*x^69 + 16*x^68 + 28*x^67 + 9*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 38*x^5 + 16*x^4 + 92*x^3 + 113*x + 16, x^73 + 60*x^71 + 116*x^70 + 78*x^69 + 92*x^68 + 76*x^67 + 108*x^66 + 49*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 78*x^5 + 28*x^4 + 12*x^3 + 44*x^2 + 25*x + 4, x^73 + 60*x^71 + 36*x^70 + 30*x^69 + 60*x^68 + 108*x^67 + 28*x^66 + 65*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 30*x^5 + 124*x^4 + 44*x^3 + 92*x^2 + 41*x + 68, x^73 + 60*x^71 + 24*x^70 + 22*x^69 + 104*x^68 + 124*x^67 + 104*x^66 + 57*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 22*x^5 + 104*x^4 + 60*x^3 + 104*x^2 + 33*x + 24, x^73 + 60*x^71 + 32*x^70 + 118*x^69 + 64*x^68 + 60*x^67 + 96*x^66 + 25*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 118*x^5 + 64*x^4 + 124*x^3 + 96*x^2 + x + 64, x^73 + 60*x^71 + 28*x^70 + 110*x^69 + 52*x^68 + 12*x^67 + 68*x^66 + 81*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 110*x^5 + 116*x^4 + 76*x^3 + 4*x^2 + 57*x + 44, x^73 + 60*x^71 + 68*x^70 + 78*x^69 + 44*x^68 + 76*x^67 + 92*x^66 + 49*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 78*x^5 + 108*x^4 + 12*x^3 + 28*x^2 + 25*x + 116, x^73 + 60*x^71 + 72*x^70 + 54*x^69 + 24*x^68 + 60*x^67 + 120*x^66 + 89*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 54*x^5 + 24*x^4 + 124*x^3 + 120*x^2 + 65*x + 40, x^73 + 60*x^71 + 56*x^70 + 70*x^69 + 56*x^68 + 92*x^67 + 104*x^66 + 41*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 70*x^5 + 56*x^4 + 28*x^3 + 104*x^2 + 17*x + 40, x^73 + 60*x^71 + 48*x^70 + 70*x^69 + 28*x^67 + 112*x^66 + 105*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 70*x^5 + 92*x^3 + 112*x^2 + 81*x + 96, x^73 + 60*x^71 + 108*x^70 + 14*x^69 + 36*x^68 + 12*x^67 + 52*x^66 + 49*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 14*x^5 + 100*x^4 + 76*x^3 + 116*x^2 + 25*x + 124, x^73 + 60*x^71 + 116*x^70 + 14*x^69 + 124*x^68 + 12*x^67 + 108*x^66 + 49*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 14*x^5 + 60*x^4 + 76*x^3 + 44*x^2 + 25*x + 100, x^73 + 60*x^71 + 68*x^70 + 110*x^69 + 76*x^68 + 12*x^67 + 28*x^66 + 81*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 110*x^5 + 12*x^4 + 76*x^3 + 92*x^2 + 57*x + 20, x^73 + 60*x^71 + 76*x^70 + 78*x^69 + 100*x^68 + 76*x^67 + 84*x^66 + 49*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 78*x^5 + 36*x^4 + 12*x^3 + 20*x^2 + 25*x + 60, x^73 + 60*x^71 + 116*x^70 + 46*x^69 + 92*x^68 + 12*x^67 + 108*x^66 + 17*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 46*x^5 + 28*x^4 + 76*x^3 + 44*x^2 + 121*x + 4, x^73 + 60*x^71 + 16*x^70 + 86*x^69 + 48*x^68 + 124*x^67 + 48*x^66 + 121*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 86*x^5 + 48*x^4 + 60*x^3 + 48*x^2 + 97*x + 16, x^73 + 60*x^71 + 96*x^70 + 22*x^69 + 32*x^68 + 124*x^67 + 96*x^66 + 57*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 22*x^5 + 32*x^4 + 60*x^3 + 96*x^2 + 33*x + 32, x^73 + 60*x^71 + 64*x^70 + 6*x^69 + 16*x^68 + 28*x^67 + 32*x^66 + 41*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 6*x^5 + 16*x^4 + 92*x^3 + 32*x^2 + 17*x + 16, x^73 + 60*x^71 + 96*x^70 + 118*x^69 + 124*x^67 + 96*x^66 + 89*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 118*x^5 + 60*x^3 + 96*x^2 + 65*x + 64, x^73 + 60*x^71 + 40*x^70 + 38*x^69 + 104*x^68 + 28*x^67 + 56*x^66 + 9*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 38*x^5 + 104*x^4 + 92*x^3 + 56*x^2 + 113*x + 56, x^73 + 60*x^71 + 20*x^70 + 94*x^69 + 76*x^68 + 44*x^67 + 108*x^66 + 65*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 94*x^5 + 12*x^4 + 108*x^3 + 44*x^2 + 41*x + 116, x^73 + 60*x^71 + 60*x^70 + 126*x^69 + 36*x^68 + 44*x^67 + 4*x^66 + 33*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 126*x^5 + 100*x^4 + 108*x^3 + 68*x^2 + 9*x + 92, x^73 + 60*x^71 + 12*x^70 + 94*x^69 + 52*x^68 + 108*x^67 + 116*x^66 + x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 94*x^5 + 116*x^4 + 44*x^3 + 52*x^2 + 105*x + 12, x^73 + 60*x^71 + 40*x^70 + 118*x^69 + 56*x^68 + 60*x^67 + 24*x^66 + 25*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 118*x^5 + 56*x^4 + 124*x^3 + 24*x^2 + x + 8, x^73 + 60*x^71 + 76*x^70 + 62*x^69 + 84*x^68 + 44*x^67 + 116*x^66 + 97*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 62*x^5 + 20*x^4 + 108*x^3 + 52*x^2 + 73*x + 44, x^73 + 60*x^71 + 32*x^70 + 118*x^69 + 64*x^68 + 124*x^67 + 32*x^66 + 89*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 118*x^5 + 64*x^4 + 60*x^3 + 32*x^2 + 65*x, x^73 + 60*x^71 + 44*x^70 + 78*x^69 + 100*x^68 + 76*x^67 + 52*x^66 + 49*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 78*x^5 + 36*x^4 + 12*x^3 + 116*x^2 + 25*x + 124, x^73 + 60*x^71 + 112*x^70 + 118*x^69 + 48*x^68 + 124*x^67 + 80*x^66 + 89*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 118*x^5 + 48*x^4 + 60*x^3 + 80*x^2 + 65*x + 16, x^73 + 60*x^71 + 64*x^70 + 70*x^69 + 48*x^68 + 92*x^67 + 32*x^66 + 41*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 70*x^5 + 48*x^4 + 28*x^3 + 32*x^2 + 17*x + 112, x^73 + 60*x^71 + 104*x^70 + 38*x^69 + 8*x^68 + 92*x^67 + 120*x^66 + 73*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 38*x^5 + 8*x^4 + 28*x^3 + 120*x^2 + 49*x + 24, x^73 + 60*x^71 + 120*x^70 + 102*x^69 + 24*x^68 + 92*x^67 + 40*x^66 + 9*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 102*x^5 + 24*x^4 + 28*x^3 + 40*x^2 + 113*x + 72, x^73 + 60*x^71 + 86*x^69 + 124*x^67 + 64*x^66 + 121*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 86*x^5 + 60*x^3 + 64*x^2 + 97*x + 64, x^73 + 60*x^71 + 88*x^70 + 22*x^69 + 104*x^68 + 60*x^67 + 104*x^66 + 121*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 22*x^5 + 104*x^4 + 124*x^3 + 104*x^2 + 97*x + 88, x^73 + 60*x^71 + 52*x^70 + 78*x^69 + 124*x^68 + 12*x^67 + 44*x^66 + 113*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 78*x^5 + 60*x^4 + 76*x^3 + 108*x^2 + 89*x + 100, x^73 + 60*x^71 + 64*x^70 + 86*x^69 + 124*x^67 + 121*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 86*x^5 + 60*x^3 + 97*x + 64, x^73 + 60*x^71 + 68*x^70 + 14*x^69 + 76*x^68 + 12*x^67 + 92*x^66 + 49*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 14*x^5 + 12*x^4 + 76*x^3 + 28*x^2 + 25*x + 84, x^73 + 60*x^71 + 52*x^70 + 62*x^69 + 12*x^68 + 108*x^67 + 12*x^66 + 33*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 62*x^5 + 76*x^4 + 44*x^3 + 76*x^2 + 9*x + 116, x^73 + 60*x^71 + 102*x^69 + 80*x^68 + 92*x^67 + 96*x^66 + 9*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 102*x^5 + 80*x^4 + 28*x^3 + 96*x^2 + 113*x + 80, x^73 + 60*x^71 + 36*x^70 + 78*x^69 + 12*x^68 + 76*x^67 + 124*x^66 + 49*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 78*x^5 + 76*x^4 + 12*x^3 + 60*x^2 + 25*x + 20, x^73 + 60*x^71 + 20*x^70 + 30*x^69 + 12*x^68 + 44*x^67 + 108*x^66 + x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 30*x^5 + 76*x^4 + 108*x^3 + 44*x^2 + 105*x + 52, x^73 + 60*x^71 + 80*x^70 + 54*x^69 + 112*x^68 + 60*x^67 + 112*x^66 + 89*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 54*x^5 + 112*x^4 + 124*x^3 + 112*x^2 + 65*x + 80, x^73 + 60*x^71 + 96*x^70 + 102*x^69 + 80*x^68 + 28*x^67 + 73*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 102*x^5 + 80*x^4 + 92*x^3 + 49*x + 80, x^73 + 60*x^71 + 92*x^70 + 62*x^69 + 68*x^68 + 44*x^67 + 100*x^66 + 97*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 62*x^5 + 4*x^4 + 108*x^3 + 36*x^2 + 73*x + 60, x^73 + 60*x^71 + 28*x^70 + 62*x^69 + 68*x^68 + 108*x^67 + 100*x^66 + 33*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 62*x^5 + 4*x^4 + 44*x^3 + 36*x^2 + 9*x + 124, x^73 + 60*x^71 + 120*x^70 + 118*x^69 + 72*x^68 + 60*x^67 + 8*x^66 + 25*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 118*x^5 + 72*x^4 + 124*x^3 + 8*x^2 + x + 56, x^73 + 60*x^71 + 120*x^70 + 102*x^69 + 56*x^68 + 28*x^67 + 40*x^66 + 73*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 102*x^5 + 56*x^4 + 92*x^3 + 40*x^2 + 49*x + 40, x^73 + 60*x^71 + 72*x^70 + 6*x^69 + 8*x^68 + 28*x^67 + 88*x^66 + 41*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 6*x^5 + 8*x^4 + 92*x^3 + 88*x^2 + 17*x + 88, x^73 + 60*x^71 + 80*x^70 + 38*x^69 + 64*x^68 + 28*x^67 + 80*x^66 + 9*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 38*x^5 + 64*x^4 + 92*x^3 + 80*x^2 + 113*x + 32, x^73 + 60*x^71 + 6*x^69 + 48*x^68 + 28*x^67 + 32*x^66 + 41*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 6*x^5 + 48*x^4 + 92*x^3 + 32*x^2 + 17*x + 48, x^73 + 60*x^71 + 56*x^70 + 6*x^69 + 88*x^68 + 92*x^67 + 40*x^66 + 105*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 6*x^5 + 88*x^4 + 28*x^3 + 40*x^2 + 81*x + 72, x^73 + 60*x^71 + 112*x^70 + 86*x^69 + 48*x^68 + 124*x^67 + 16*x^66 + 121*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 86*x^5 + 48*x^4 + 60*x^3 + 16*x^2 + 97*x + 80, x^73 + 60*x^71 + 64*x^70 + 70*x^69 + 112*x^68 + 92*x^67 + 32*x^66 + 41*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 70*x^5 + 112*x^4 + 28*x^3 + 32*x^2 + 17*x + 48, x^73 + 60*x^71 + 52*x^70 + 46*x^69 + 28*x^68 + 76*x^67 + 108*x^66 + 81*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 46*x^5 + 92*x^4 + 12*x^3 + 44*x^2 + 57*x + 4, x^73 + 60*x^71 + 120*x^70 + 6*x^69 + 56*x^68 + 28*x^67 + 104*x^66 + 41*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 6*x^5 + 56*x^4 + 92*x^3 + 104*x^2 + 17*x + 104, x^73 + 60*x^71 + 84*x^70 + 110*x^69 + 28*x^68 + 76*x^67 + 12*x^66 + 17*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 110*x^5 + 92*x^4 + 12*x^3 + 76*x^2 + 121*x + 68, x^73 + 60*x^71 + 96*x^70 + 86*x^69 + 64*x^68 + 124*x^67 + 32*x^66 + 121*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 86*x^5 + 64*x^4 + 60*x^3 + 32*x^2 + 97*x + 64, x^73 + 60*x^71 + 12*x^70 + 94*x^69 + 84*x^68 + 44*x^67 + 116*x^66 + 65*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 94*x^5 + 20*x^4 + 108*x^3 + 52*x^2 + 41*x + 108, x^73 + 60*x^71 + 16*x^70 + 54*x^69 + 112*x^68 + 124*x^67 + 112*x^66 + 25*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 54*x^5 + 112*x^4 + 60*x^3 + 112*x^2 + x + 16, x^73 + 60*x^71 + 60*x^70 + 62*x^69 + 36*x^68 + 108*x^67 + 68*x^66 + 33*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 62*x^5 + 100*x^4 + 44*x^3 + 4*x^2 + 9*x + 28, x^73 + 60*x^71 + 116*x^70 + 94*x^69 + 44*x^68 + 108*x^67 + 76*x^66 + x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 94*x^5 + 108*x^4 + 44*x^3 + 12*x^2 + 105*x + 84, x^73 + 60*x^71 + 68*x^70 + 110*x^69 + 108*x^68 + 76*x^67 + 28*x^66 + 17*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 110*x^5 + 44*x^4 + 12*x^3 + 92*x^2 + 121*x + 116, x^73 + 60*x^71 + 36*x^70 + 62*x^69 + 124*x^68 + 108*x^67 + 92*x^66 + 33*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 62*x^5 + 60*x^4 + 44*x^3 + 28*x^2 + 9*x + 68, x^73 + 60*x^71 + 80*x^70 + 118*x^69 + 80*x^68 + 124*x^67 + 112*x^66 + 89*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 118*x^5 + 80*x^4 + 60*x^3 + 112*x^2 + 65*x + 112, x^73 + 60*x^71 + 112*x^70 + 118*x^69 + 16*x^68 + 60*x^67 + 80*x^66 + 25*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 118*x^5 + 16*x^4 + 124*x^3 + 80*x^2 + x + 48, x^73 + 60*x^71 + 4*x^70 + 62*x^69 + 92*x^68 + 108*x^67 + 124*x^66 + 33*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 62*x^5 + 28*x^4 + 44*x^3 + 60*x^2 + 9*x + 100, x^73 + 60*x^71 + 104*x^70 + 38*x^69 + 40*x^68 + 92*x^67 + 56*x^66 + 73*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 38*x^5 + 40*x^4 + 28*x^3 + 56*x^2 + 49*x + 56, x^73 + 60*x^71 + 20*x^70 + 126*x^69 + 76*x^68 + 108*x^67 + 108*x^66 + 97*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 126*x^5 + 12*x^4 + 44*x^3 + 44*x^2 + 73*x + 116, x^73 + 60*x^71 + 8*x^70 + 86*x^69 + 88*x^68 + 60*x^67 + 120*x^66 + 57*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 86*x^5 + 88*x^4 + 124*x^3 + 120*x^2 + 33*x + 40, x^73 + 60*x^71 + 40*x^70 + 54*x^69 + 120*x^68 + 124*x^67 + 88*x^66 + 25*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 54*x^5 + 120*x^4 + 60*x^3 + 88*x^2 + x + 8, x^73 + 60*x^71 + 120*x^70 + 38*x^69 + 24*x^68 + 92*x^67 + 40*x^66 + 73*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 38*x^5 + 24*x^4 + 28*x^3 + 40*x^2 + 49*x + 72, x^73 + 60*x^71 + 108*x^70 + 30*x^69 + 84*x^68 + 108*x^67 + 20*x^66 + 65*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 30*x^5 + 20*x^4 + 44*x^3 + 84*x^2 + 41*x + 108, x^73 + 60*x^71 + 54*x^69 + 64*x^68 + 60*x^67 + 64*x^66 + 89*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 54*x^5 + 64*x^4 + 124*x^3 + 64*x^2 + 65*x, x^73 + 60*x^71 + 44*x^70 + 110*x^69 + 100*x^68 + 76*x^67 + 116*x^66 + 17*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 110*x^5 + 36*x^4 + 12*x^3 + 52*x^2 + 121*x + 60, x^73 + 60*x^71 + 16*x^70 + 118*x^69 + 112*x^68 + 124*x^67 + 112*x^66 + 89*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 118*x^5 + 112*x^4 + 60*x^3 + 112*x^2 + 65*x + 16, x^73 + 60*x^71 + 8*x^70 + 102*x^69 + 72*x^68 + 28*x^67 + 88*x^66 + 73*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 102*x^5 + 72*x^4 + 92*x^3 + 88*x^2 + 49*x + 88, x^73 + 60*x^71 + 40*x^70 + 38*x^69 + 40*x^68 + 92*x^67 + 120*x^66 + 73*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 38*x^5 + 40*x^4 + 28*x^3 + 120*x^2 + 49*x + 56, x^73 + 60*x^71 + 8*x^70 + 38*x^69 + 72*x^68 + 28*x^67 + 88*x^66 + 9*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 38*x^5 + 72*x^4 + 92*x^3 + 88*x^2 + 113*x + 88, x^73 + 60*x^71 + 24*x^70 + 86*x^69 + 8*x^68 + 124*x^67 + 40*x^66 + 121*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 86*x^5 + 8*x^4 + 60*x^3 + 40*x^2 + 97*x + 56, x^73 + 60*x^71 + 116*x^70 + 14*x^69 + 60*x^68 + 76*x^67 + 44*x^66 + 113*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 14*x^5 + 124*x^4 + 12*x^3 + 108*x^2 + 89*x + 100, x^73 + 60*x^71 + 120*x^70 + 70*x^69 + 56*x^68 + 92*x^67 + 40*x^66 + 41*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 70*x^5 + 56*x^4 + 28*x^3 + 40*x^2 + 17*x + 40, x^73 + 60*x^71 + 48*x^70 + 102*x^69 + 96*x^68 + 92*x^67 + 48*x^66 + 9*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 102*x^5 + 96*x^4 + 28*x^3 + 48*x^2 + 113*x + 64, x^73 + 60*x^71 + 52*x^70 + 126*x^69 + 108*x^68 + 108*x^67 + 76*x^66 + 97*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 126*x^5 + 44*x^4 + 44*x^3 + 12*x^2 + 73*x + 84, x^73 + 60*x^71 + 108*x^70 + 46*x^69 + 36*x^68 + 76*x^67 + 52*x^66 + 81*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 46*x^5 + 100*x^4 + 12*x^3 + 116*x^2 + 57*x + 124, x^73 + 60*x^71 + 88*x^70 + 6*x^69 + 120*x^68 + 92*x^67 + 8*x^66 + 105*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 6*x^5 + 120*x^4 + 28*x^3 + 8*x^2 + 81*x + 40, x^73 + 60*x^71 + 112*x^70 + 70*x^69 + 32*x^68 + 28*x^67 + 112*x^66 + 105*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 70*x^5 + 32*x^4 + 92*x^3 + 112*x^2 + 81*x, x^73 + 60*x^71 + 48*x^70 + 22*x^69 + 48*x^68 + 60*x^67 + 16*x^66 + 121*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 22*x^5 + 48*x^4 + 124*x^3 + 16*x^2 + 97*x + 16, x^73 + 60*x^71 + 40*x^70 + 6*x^69 + 72*x^68 + 28*x^67 + 56*x^66 + 41*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 6*x^5 + 72*x^4 + 92*x^3 + 56*x^2 + 17*x + 88, x^73 + 60*x^71 + 24*x^70 + 70*x^69 + 56*x^68 + 28*x^67 + 8*x^66 + 105*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 70*x^5 + 56*x^4 + 92*x^3 + 8*x^2 + 81*x + 40, x^73 + 60*x^71 + 16*x^70 + 102*x^69 + 92*x^67 + 80*x^66 + 9*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 102*x^5 + 28*x^3 + 80*x^2 + 113*x + 32, x^73 + 60*x^71 + 60*x^70 + 62*x^69 + 4*x^68 + 108*x^67 + 4*x^66 + 33*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 62*x^5 + 68*x^4 + 44*x^3 + 68*x^2 + 9*x + 124, x^73 + 60*x^71 + 64*x^70 + 6*x^69 + 80*x^68 + 28*x^67 + 32*x^66 + 41*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 6*x^5 + 80*x^4 + 92*x^3 + 32*x^2 + 17*x + 80, x^73 + 60*x^71 + 68*x^70 + 14*x^69 + 76*x^68 + 76*x^67 + 28*x^66 + 113*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 14*x^5 + 12*x^4 + 12*x^3 + 92*x^2 + 89*x + 20, x^73 + 60*x^71 + 32*x^70 + 70*x^69 + 16*x^68 + 92*x^67 + 64*x^66 + 41*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 70*x^5 + 16*x^4 + 28*x^3 + 64*x^2 + 17*x + 16, x^73 + 60*x^71 + 104*x^70 + 38*x^69 + 40*x^68 + 28*x^67 + 120*x^66 + 9*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 38*x^5 + 40*x^4 + 92*x^3 + 120*x^2 + 113*x + 120, x^73 + 60*x^71 + 84*x^70 + 30*x^69 + 44*x^68 + 44*x^67 + 108*x^66 + x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 30*x^5 + 108*x^4 + 108*x^3 + 44*x^2 + 105*x + 84, x^73 + 60*x^71 + 120*x^70 + 86*x^69 + 72*x^68 + 60*x^67 + 72*x^66 + 57*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 86*x^5 + 72*x^4 + 124*x^3 + 72*x^2 + 33*x + 120, x^73 + 60*x^71 + 16*x^70 + 102*x^69 + 64*x^68 + 92*x^67 + 80*x^66 + 9*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 102*x^5 + 64*x^4 + 28*x^3 + 80*x^2 + 113*x + 96, x^73 + 60*x^71 + 52*x^70 + 14*x^69 + 124*x^68 + 12*x^67 + 44*x^66 + 49*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 14*x^5 + 60*x^4 + 76*x^3 + 108*x^2 + 25*x + 100, x^73 + 60*x^71 + 12*x^70 + 94*x^69 + 52*x^68 + 44*x^67 + 52*x^66 + 65*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 94*x^5 + 116*x^4 + 108*x^3 + 116*x^2 + 41*x + 76, x^73 + 60*x^71 + 84*x^70 + 110*x^69 + 60*x^68 + 76*x^67 + 76*x^66 + 17*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 110*x^5 + 124*x^4 + 12*x^3 + 12*x^2 + 121*x + 100, x^73 + 60*x^71 + 20*x^70 + 94*x^69 + 12*x^68 + 44*x^67 + 108*x^66 + 65*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 94*x^5 + 76*x^4 + 108*x^3 + 44*x^2 + 41*x + 52, x^73 + 60*x^71 + 60*x^70 + 46*x^69 + 20*x^68 + 76*x^67 + 100*x^66 + 81*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 46*x^5 + 84*x^4 + 12*x^3 + 36*x^2 + 57*x + 12, x^73 + 60*x^71 + 80*x^70 + 6*x^69 + 96*x^68 + 28*x^67 + 80*x^66 + 41*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 6*x^5 + 96*x^4 + 92*x^3 + 80*x^2 + 17*x, x^73 + 60*x^71 + 44*x^70 + 78*x^69 + 4*x^68 + 12*x^67 + 52*x^66 + 113*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 78*x^5 + 68*x^4 + 76*x^3 + 116*x^2 + 89*x + 92, x^73 + 60*x^71 + 32*x^70 + 38*x^69 + 80*x^68 + 92*x^67 + 73*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 38*x^5 + 80*x^4 + 28*x^3 + 49*x + 16, x^73 + 60*x^71 + 40*x^70 + 102*x^69 + 72*x^68 + 28*x^67 + 120*x^66 + 73*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 102*x^5 + 72*x^4 + 92*x^3 + 120*x^2 + 49*x + 24, x^73 + 60*x^71 + 8*x^70 + 54*x^69 + 24*x^68 + 60*x^67 + 56*x^66 + 89*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 54*x^5 + 24*x^4 + 124*x^3 + 56*x^2 + 65*x + 40, x^73 + 60*x^71 + 104*x^70 + 38*x^69 + 72*x^68 + 92*x^67 + 120*x^66 + 73*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 38*x^5 + 72*x^4 + 28*x^3 + 120*x^2 + 49*x + 88, x^73 + 60*x^71 + 8*x^70 + 102*x^69 + 104*x^68 + 28*x^67 + 24*x^66 + 73*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 102*x^5 + 104*x^4 + 92*x^3 + 24*x^2 + 49*x + 120, x^73 + 60*x^71 + 92*x^70 + 110*x^69 + 116*x^68 + 76*x^67 + 68*x^66 + 17*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 110*x^5 + 52*x^4 + 12*x^3 + 4*x^2 + 121*x + 44, x^73 + 60*x^71 + 104*x^70 + 102*x^69 + 40*x^68 + 92*x^67 + 56*x^66 + 9*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 102*x^5 + 40*x^4 + 28*x^3 + 56*x^2 + 113*x + 56, x^73 + 60*x^71 + 100*x^70 + 78*x^69 + 76*x^68 + 76*x^67 + 60*x^66 + 49*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 78*x^5 + 12*x^4 + 12*x^3 + 124*x^2 + 25*x + 84, x^73 + 60*x^71 + 80*x^70 + 102*x^69 + 92*x^67 + 16*x^66 + 9*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 102*x^5 + 28*x^3 + 16*x^2 + 113*x + 32, x^73 + 60*x^71 + 88*x^70 + 22*x^69 + 40*x^68 + 60*x^67 + 104*x^66 + 121*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 22*x^5 + 40*x^4 + 124*x^3 + 104*x^2 + 97*x + 24, x^73 + 60*x^71 + 112*x^70 + 70*x^69 + 96*x^68 + 92*x^67 + 48*x^66 + 41*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 70*x^5 + 96*x^4 + 28*x^3 + 48*x^2 + 17*x, x^73 + 60*x^71 + 60*x^70 + 30*x^69 + 68*x^68 + 44*x^67 + 4*x^66 + x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 30*x^5 + 4*x^4 + 108*x^3 + 68*x^2 + 105*x + 60, x^73 + 60*x^71 + 28*x^70 + 126*x^69 + 4*x^68 + 44*x^67 + 36*x^66 + 33*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 126*x^5 + 68*x^4 + 108*x^3 + 100*x^2 + 9*x + 124, x^73 + 60*x^71 + 120*x^70 + 22*x^69 + 104*x^68 + 124*x^67 + 72*x^66 + 57*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 22*x^5 + 104*x^4 + 60*x^3 + 72*x^2 + 33*x + 88, x^73 + 60*x^71 + 56*x^70 + 118*x^69 + 8*x^68 + 124*x^67 + 8*x^66 + 89*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 118*x^5 + 8*x^4 + 60*x^3 + 8*x^2 + 65*x + 56, x^73 + 60*x^71 + 116*x^70 + 30*x^69 + 108*x^68 + 108*x^67 + 76*x^66 + 65*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 30*x^5 + 44*x^4 + 44*x^3 + 12*x^2 + 41*x + 20, x^73 + 60*x^71 + 12*x^70 + 62*x^69 + 52*x^68 + 44*x^67 + 116*x^66 + 97*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 62*x^5 + 116*x^4 + 108*x^3 + 52*x^2 + 73*x + 12, x^73 + 60*x^71 + 116*x^70 + 126*x^69 + 12*x^68 + 108*x^67 + 76*x^66 + 97*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 126*x^5 + 76*x^4 + 44*x^3 + 12*x^2 + 73*x + 116, x^73 + 60*x^71 + 112*x^70 + 22*x^69 + 16*x^68 + 124*x^67 + 80*x^66 + 57*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 22*x^5 + 16*x^4 + 60*x^3 + 80*x^2 + 33*x + 48, x^73 + 60*x^71 + 104*x^70 + 54*x^69 + 120*x^68 + 60*x^67 + 88*x^66 + 89*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 54*x^5 + 120*x^4 + 124*x^3 + 88*x^2 + 65*x + 72, x^73 + 60*x^71 + 28*x^70 + 14*x^69 + 84*x^68 + 76*x^67 + 4*x^66 + 113*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 14*x^5 + 20*x^4 + 12*x^3 + 68*x^2 + 89*x + 76, x^73 + 60*x^71 + 52*x^70 + 30*x^69 + 12*x^68 + 108*x^67 + 76*x^66 + 65*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 30*x^5 + 76*x^4 + 44*x^3 + 12*x^2 + 41*x + 52, x^73 + 60*x^71 + 108*x^70 + 62*x^69 + 20*x^68 + 108*x^67 + 84*x^66 + 33*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 62*x^5 + 84*x^4 + 44*x^3 + 20*x^2 + 9*x + 108, x^73 + 60*x^71 + 32*x^70 + 70*x^69 + 48*x^68 + 92*x^67 + 41*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 70*x^5 + 48*x^4 + 28*x^3 + 17*x + 48, x^73 + 60*x^71 + 112*x^70 + 86*x^69 + 112*x^68 + 124*x^67 + 16*x^66 + 121*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 86*x^5 + 112*x^4 + 60*x^3 + 16*x^2 + 97*x + 16, x^73 + 60*x^71 + 108*x^70 + 94*x^69 + 20*x^68 + 108*x^67 + 20*x^66 + x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 94*x^5 + 84*x^4 + 44*x^3 + 84*x^2 + 105*x + 44, x^73 + 60*x^71 + 72*x^70 + 38*x^69 + 8*x^68 + 92*x^67 + 88*x^66 + 73*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 38*x^5 + 8*x^4 + 28*x^3 + 88*x^2 + 49*x + 88, x^73 + 60*x^71 + 56*x^70 + 118*x^69 + 72*x^68 + 60*x^67 + 72*x^66 + 25*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 118*x^5 + 72*x^4 + 124*x^3 + 72*x^2 + x + 56, x^73 + 60*x^71 + 116*x^70 + 62*x^69 + 44*x^68 + 44*x^67 + 76*x^66 + 97*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 62*x^5 + 108*x^4 + 108*x^3 + 12*x^2 + 73*x + 84, x^73 + 60*x^71 + 100*x^70 + 62*x^69 + 28*x^68 + 108*x^67 + 92*x^66 + 33*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 62*x^5 + 92*x^4 + 44*x^3 + 28*x^2 + 9*x + 100, x^73 + 60*x^71 + 36*x^70 + 46*x^69 + 12*x^68 + 12*x^67 + 124*x^66 + 17*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 46*x^5 + 76*x^4 + 76*x^3 + 60*x^2 + 121*x + 20, x^73 + 60*x^71 + 92*x^70 + 126*x^69 + 36*x^68 + 44*x^67 + 36*x^66 + 33*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 126*x^5 + 100*x^4 + 108*x^3 + 100*x^2 + 9*x + 28, x^73 + 60*x^71 + 84*x^70 + 14*x^69 + 28*x^68 + 76*x^67 + 76*x^66 + 113*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 14*x^5 + 92*x^4 + 12*x^3 + 12*x^2 + 89*x + 4, x^73 + 60*x^71 + 56*x^70 + 102*x^69 + 120*x^68 + 28*x^67 + 104*x^66 + 73*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 102*x^5 + 120*x^4 + 92*x^3 + 104*x^2 + 49*x + 104, x^73 + 60*x^71 + 12*x^70 + 110*x^69 + 36*x^68 + 76*x^67 + 84*x^66 + 17*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 110*x^5 + 100*x^4 + 12*x^3 + 20*x^2 + 121*x + 60, x^73 + 60*x^71 + 16*x^70 + 118*x^69 + 80*x^68 + 124*x^67 + 48*x^66 + 89*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 118*x^5 + 80*x^4 + 60*x^3 + 48*x^2 + 65*x + 112, x^73 + 60*x^71 + 8*x^70 + 102*x^69 + 8*x^68 + 28*x^67 + 88*x^66 + 73*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 102*x^5 + 8*x^4 + 92*x^3 + 88*x^2 + 49*x + 24, x^73 + 60*x^71 + 12*x^70 + 110*x^69 + 36*x^68 + 12*x^67 + 20*x^66 + 81*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 110*x^5 + 100*x^4 + 76*x^3 + 84*x^2 + 57*x + 124, x^73 + 60*x^71 + 22*x^69 + 64*x^68 + 124*x^67 + 64*x^66 + 57*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 22*x^5 + 64*x^4 + 60*x^3 + 64*x^2 + 33*x, x^73 + 60*x^71 + 104*x^70 + 70*x^69 + 104*x^68 + 28*x^67 + 56*x^66 + 105*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 70*x^5 + 104*x^4 + 92*x^3 + 56*x^2 + 81*x + 120, x^73 + 60*x^71 + 4*x^70 + 94*x^69 + 124*x^68 + 44*x^67 + 60*x^66 + 65*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 94*x^5 + 60*x^4 + 108*x^3 + 124*x^2 + 41*x + 4, x^73 + 60*x^71 + 52*x^70 + 46*x^69 + 92*x^68 + 76*x^67 + 108*x^66 + 81*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 46*x^5 + 28*x^4 + 12*x^3 + 44*x^2 + 57*x + 68, x^73 + 60*x^71 + 64*x^70 + 22*x^69 + 64*x^68 + 124*x^67 + 57*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 22*x^5 + 64*x^4 + 60*x^3 + 33*x, x^73 + 60*x^71 + 56*x^70 + 54*x^69 + 72*x^68 + 60*x^67 + 72*x^66 + 89*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 54*x^5 + 72*x^4 + 124*x^3 + 72*x^2 + 65*x + 56, x^73 + 60*x^71 + 8*x^70 + 86*x^69 + 24*x^68 + 124*x^67 + 56*x^66 + 121*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 86*x^5 + 24*x^4 + 60*x^3 + 56*x^2 + 97*x + 40, x^73 + 60*x^71 + 76*x^70 + 94*x^69 + 52*x^68 + 44*x^67 + 116*x^66 + 65*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 94*x^5 + 116*x^4 + 108*x^3 + 52*x^2 + 41*x + 76, x^73 + 60*x^71 + 80*x^70 + 102*x^69 + 64*x^68 + 92*x^67 + 16*x^66 + 9*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 102*x^5 + 64*x^4 + 28*x^3 + 16*x^2 + 113*x + 96, x^73 + 60*x^71 + 8*x^70 + 22*x^69 + 56*x^68 + 124*x^67 + 120*x^66 + 57*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 22*x^5 + 56*x^4 + 60*x^3 + 120*x^2 + 33*x + 72, x^73 + 60*x^71 + 60*x^70 + 110*x^69 + 84*x^68 + 76*x^67 + 100*x^66 + 17*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 110*x^5 + 20*x^4 + 12*x^3 + 36*x^2 + 121*x + 76, x^73 + 60*x^71 + 40*x^70 + 102*x^69 + 104*x^68 + 28*x^67 + 56*x^66 + 73*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 102*x^5 + 104*x^4 + 92*x^3 + 56*x^2 + 49*x + 56, x^73 + 60*x^71 + 28*x^70 + 110*x^69 + 20*x^68 + 76*x^67 + 68*x^66 + 17*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 110*x^5 + 84*x^4 + 12*x^3 + 4*x^2 + 121*x + 76, x^73 + 60*x^71 + 112*x^70 + 118*x^69 + 112*x^68 + 124*x^67 + 80*x^66 + 89*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 118*x^5 + 112*x^4 + 60*x^3 + 80*x^2 + 65*x + 80, x^73 + 60*x^71 + 108*x^70 + 46*x^69 + 100*x^68 + 76*x^67 + 52*x^66 + 81*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 46*x^5 + 36*x^4 + 12*x^3 + 116*x^2 + 57*x + 60, x^73 + 60*x^71 + 84*x^70 + 78*x^69 + 60*x^68 + 12*x^67 + 76*x^66 + 113*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 78*x^5 + 124*x^4 + 76*x^3 + 12*x^2 + 89*x + 100, x^73 + 60*x^71 + 72*x^70 + 70*x^69 + 8*x^68 + 28*x^67 + 88*x^66 + 105*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 70*x^5 + 8*x^4 + 92*x^3 + 88*x^2 + 81*x + 88, x^73 + 60*x^71 + 120*x^70 + 118*x^69 + 40*x^68 + 124*x^67 + 8*x^66 + 89*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 118*x^5 + 40*x^4 + 60*x^3 + 8*x^2 + 65*x + 88, x^73 + 60*x^71 + 68*x^70 + 30*x^69 + 60*x^68 + 108*x^67 + 60*x^66 + 65*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 30*x^5 + 124*x^4 + 44*x^3 + 124*x^2 + 41*x + 4, x^73 + 60*x^71 + 12*x^70 + 62*x^69 + 116*x^68 + 108*x^67 + 52*x^66 + 33*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 62*x^5 + 52*x^4 + 44*x^3 + 116*x^2 + 9*x + 12, x^73 + 60*x^71 + 112*x^70 + 54*x^69 + 48*x^68 + 124*x^67 + 80*x^66 + 25*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 54*x^5 + 48*x^4 + 60*x^3 + 80*x^2 + x + 16, x^73 + 60*x^71 + 92*x^70 + 78*x^69 + 116*x^68 + 12*x^67 + 68*x^66 + 113*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 78*x^5 + 52*x^4 + 76*x^3 + 4*x^2 + 89*x + 44, x^73 + 60*x^71 + 52*x^70 + 94*x^69 + 76*x^68 + 108*x^67 + 76*x^66 + x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 94*x^5 + 12*x^4 + 44*x^3 + 12*x^2 + 105*x + 116, x^73 + 60*x^71 + 36*x^70 + 46*x^69 + 76*x^68 + 12*x^67 + 124*x^66 + 17*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 46*x^5 + 12*x^4 + 76*x^3 + 60*x^2 + 121*x + 84, x^73 + 60*x^71 + 48*x^70 + 38*x^69 + 28*x^67 + 48*x^66 + 9*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 38*x^5 + 92*x^3 + 48*x^2 + 113*x + 32, x^73 + 60*x^71 + 76*x^70 + 14*x^69 + 100*x^68 + 12*x^67 + 20*x^66 + 49*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 14*x^5 + 36*x^4 + 76*x^3 + 84*x^2 + 25*x + 124, x^73 + 60*x^71 + 4*x^70 + 46*x^69 + 12*x^68 + 76*x^67 + 28*x^66 + 81*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 46*x^5 + 76*x^4 + 12*x^3 + 92*x^2 + 57*x + 20, x^73 + 60*x^71 + 92*x^70 + 126*x^69 + 4*x^68 + 44*x^67 + 100*x^66 + 33*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 126*x^5 + 68*x^4 + 108*x^3 + 36*x^2 + 9*x + 124, x^73 + 60*x^71 + 24*x^70 + 118*x^69 + 104*x^68 + 60*x^67 + 104*x^66 + 25*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 118*x^5 + 104*x^4 + 124*x^3 + 104*x^2 + x + 24, x^73 + 60*x^71 + 52*x^70 + 94*x^69 + 44*x^68 + 44*x^67 + 76*x^66 + 65*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 94*x^5 + 108*x^4 + 108*x^3 + 12*x^2 + 41*x + 20, x^73 + 60*x^71 + 32*x^70 + 70*x^69 + 80*x^68 + 92*x^67 + 64*x^66 + 41*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 70*x^5 + 80*x^4 + 28*x^3 + 64*x^2 + 17*x + 80, x^73 + 60*x^71 + 88*x^70 + 22*x^69 + 72*x^68 + 124*x^67 + 104*x^66 + 57*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 22*x^5 + 72*x^4 + 60*x^3 + 104*x^2 + 33*x + 120, x^73 + 60*x^71 + 20*x^70 + 94*x^69 + 44*x^68 + 44*x^67 + 44*x^66 + 65*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 94*x^5 + 108*x^4 + 108*x^3 + 108*x^2 + 41*x + 84, x^73 + 60*x^71 + 84*x^70 + 94*x^69 + 12*x^68 + 44*x^67 + 44*x^66 + 65*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 94*x^5 + 76*x^4 + 108*x^3 + 108*x^2 + 41*x + 52, x^73 + 60*x^71 + 12*x^70 + 94*x^69 + 116*x^68 + 44*x^67 + 52*x^66 + 65*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 94*x^5 + 52*x^4 + 108*x^3 + 116*x^2 + 41*x + 12, x^73 + 60*x^71 + 92*x^70 + 94*x^69 + 68*x^68 + 44*x^67 + 36*x^66 + 65*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 94*x^5 + 4*x^4 + 108*x^3 + 100*x^2 + 41*x + 124, x^73 + 60*x^71 + 124*x^70 + 30*x^69 + 4*x^68 + 108*x^67 + 4*x^66 + 65*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 30*x^5 + 68*x^4 + 44*x^3 + 68*x^2 + 41*x + 60, x^73 + 60*x^71 + 88*x^70 + 38*x^69 + 24*x^68 + 92*x^67 + 8*x^66 + 73*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 38*x^5 + 24*x^4 + 28*x^3 + 8*x^2 + 49*x + 8, x^73 + 60*x^71 + 20*x^70 + 14*x^69 + 124*x^68 + 12*x^67 + 12*x^66 + 49*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 14*x^5 + 60*x^4 + 76*x^3 + 76*x^2 + 25*x + 36, x^73 + 60*x^71 + 60*x^70 + 78*x^69 + 52*x^68 + 12*x^67 + 36*x^66 + 113*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 78*x^5 + 116*x^4 + 76*x^3 + 100*x^2 + 89*x + 44, x^73 + 60*x^71 + 48*x^70 + 102*x^69 + 32*x^68 + 28*x^67 + 112*x^66 + 73*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 102*x^5 + 32*x^4 + 92*x^3 + 112*x^2 + 49*x + 64, x^73 + 60*x^71 + 28*x^70 + 126*x^69 + 36*x^68 + 108*x^67 + 36*x^66 + 97*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 126*x^5 + 100*x^4 + 44*x^3 + 100*x^2 + 73*x + 92, x^73 + 60*x^71 + 20*x^70 + 94*x^69 + 44*x^68 + 108*x^67 + 108*x^66 + x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 94*x^5 + 108*x^4 + 44*x^3 + 44*x^2 + 105*x + 20, x^73 + 60*x^71 + 100*x^70 + 126*x^69 + 124*x^68 + 44*x^67 + 92*x^66 + 33*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 126*x^5 + 60*x^4 + 108*x^3 + 28*x^2 + 9*x + 4, x^73 + 60*x^71 + 100*x^70 + 30*x^69 + 92*x^68 + 44*x^67 + 92*x^66 + x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 30*x^5 + 28*x^4 + 108*x^3 + 28*x^2 + 105*x + 36, x^73 + 60*x^71 + 36*x^70 + 30*x^69 + 28*x^68 + 44*x^67 + 28*x^66 + x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 30*x^5 + 92*x^4 + 108*x^3 + 92*x^2 + 105*x + 100, x^73 + 60*x^71 + 28*x^70 + 30*x^69 + 68*x^68 + 44*x^67 + 100*x^66 + x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 30*x^5 + 4*x^4 + 108*x^3 + 36*x^2 + 105*x + 124, x^73 + 60*x^71 + 68*x^70 + 14*x^69 + 44*x^68 + 12*x^67 + 28*x^66 + 49*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 14*x^5 + 108*x^4 + 76*x^3 + 92*x^2 + 25*x + 52, x^73 + 60*x^71 + 84*x^70 + 126*x^69 + 12*x^68 + 44*x^67 + 108*x^66 + 33*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 126*x^5 + 76*x^4 + 108*x^3 + 44*x^2 + 9*x + 116, x^73 + 60*x^71 + 124*x^70 + 14*x^69 + 52*x^68 + 76*x^67 + 36*x^66 + 113*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 14*x^5 + 116*x^4 + 12*x^3 + 100*x^2 + 89*x + 108, x^73 + 60*x^71 + 80*x^70 + 102*x^69 + 96*x^68 + 28*x^67 + 16*x^66 + 73*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 102*x^5 + 96*x^4 + 92*x^3 + 16*x^2 + 49*x + 64, x^73 + 60*x^71 + 60*x^70 + 46*x^69 + 116*x^68 + 76*x^67 + 36*x^66 + 81*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 46*x^5 + 52*x^4 + 12*x^3 + 100*x^2 + 57*x + 108, x^73 + 60*x^71 + 8*x^70 + 70*x^69 + 104*x^68 + 28*x^67 + 88*x^66 + 105*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 70*x^5 + 104*x^4 + 92*x^3 + 88*x^2 + 81*x + 56, x^73 + 60*x^71 + 36*x^70 + 46*x^69 + 76*x^68 + 76*x^67 + 60*x^66 + 81*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 46*x^5 + 12*x^4 + 12*x^3 + 124*x^2 + 57*x + 20, x^73 + 60*x^71 + 116*x^70 + 78*x^69 + 60*x^68 + 12*x^67 + 108*x^66 + 113*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 78*x^5 + 124*x^4 + 76*x^3 + 44*x^2 + 89*x + 36, x^73 + 60*x^71 + 24*x^70 + 6*x^69 + 120*x^68 + 28*x^67 + 8*x^66 + 41*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 6*x^5 + 120*x^4 + 92*x^3 + 8*x^2 + 17*x + 104, x^73 + 60*x^71 + 84*x^70 + 46*x^69 + 124*x^68 + 76*x^67 + 76*x^66 + 81*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 46*x^5 + 60*x^4 + 12*x^3 + 12*x^2 + 57*x + 36, x^73 + 60*x^71 + 108*x^70 + 78*x^69 + 4*x^68 + 12*x^67 + 116*x^66 + 113*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 78*x^5 + 68*x^4 + 76*x^3 + 52*x^2 + 89*x + 92, x^73 + 60*x^71 + 100*x^70 + 94*x^69 + 60*x^68 + 108*x^67 + 92*x^66 + x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 94*x^5 + 124*x^4 + 44*x^3 + 28*x^2 + 105*x + 68, x^73 + 60*x^71 + 80*x^70 + 54*x^69 + 80*x^68 + 124*x^67 + 112*x^66 + 25*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 54*x^5 + 80*x^4 + 60*x^3 + 112*x^2 + x + 112, x^73 + 60*x^71 + 112*x^70 + 102*x^69 + 28*x^67 + 112*x^66 + 73*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 102*x^5 + 92*x^3 + 112*x^2 + 49*x + 32, x^73 + 60*x^71 + 12*x^70 + 78*x^69 + 36*x^68 + 12*x^67 + 84*x^66 + 113*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 78*x^5 + 100*x^4 + 76*x^3 + 20*x^2 + 89*x + 60, x^73 + 60*x^71 + 120*x^70 + 54*x^69 + 72*x^68 + 60*x^67 + 8*x^66 + 89*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 54*x^5 + 72*x^4 + 124*x^3 + 8*x^2 + 65*x + 56, x^73 + 60*x^71 + 12*x^70 + 126*x^69 + 84*x^68 + 44*x^67 + 52*x^66 + 33*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 126*x^5 + 20*x^4 + 108*x^3 + 116*x^2 + 9*x + 44, x^73 + 60*x^71 + 124*x^70 + 78*x^69 + 20*x^68 + 76*x^67 + 100*x^66 + 49*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 78*x^5 + 84*x^4 + 12*x^3 + 36*x^2 + 25*x + 76, x^73 + 60*x^71 + 4*x^70 + 126*x^69 + 60*x^68 + 44*x^67 + 124*x^66 + 33*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 126*x^5 + 124*x^4 + 108*x^3 + 60*x^2 + 9*x + 4, x^73 + 60*x^71 + 112*x^70 + 102*x^69 + 64*x^68 + 28*x^67 + 112*x^66 + 73*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 102*x^5 + 64*x^4 + 92*x^3 + 112*x^2 + 49*x + 96, x^73 + 60*x^71 + 92*x^70 + 14*x^69 + 20*x^68 + 76*x^67 + 68*x^66 + 113*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 14*x^5 + 84*x^4 + 12*x^3 + 4*x^2 + 89*x + 12, x^73 + 60*x^71 + 100*x^70 + 14*x^69 + 108*x^68 + 76*x^67 + 124*x^66 + 113*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 14*x^5 + 44*x^4 + 12*x^3 + 60*x^2 + 89*x + 116, x^73 + 60*x^71 + 4*x^70 + 126*x^69 + 28*x^68 + 108*x^67 + 124*x^66 + 97*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 126*x^5 + 92*x^4 + 44*x^3 + 60*x^2 + 73*x + 36, x^73 + 60*x^71 + 12*x^70 + 46*x^69 + 4*x^68 + 76*x^67 + 20*x^66 + 81*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 46*x^5 + 68*x^4 + 12*x^3 + 84*x^2 + 57*x + 28, x^73 + 60*x^71 + 76*x^70 + 126*x^69 + 116*x^68 + 108*x^67 + 116*x^66 + 97*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 126*x^5 + 52*x^4 + 44*x^3 + 52*x^2 + 73*x + 12, x^73 + 60*x^71 + 16*x^70 + 38*x^69 + 96*x^68 + 92*x^67 + 16*x^66 + 73*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 38*x^5 + 96*x^4 + 28*x^3 + 16*x^2 + 49*x, x^73 + 60*x^71 + 80*x^70 + 22*x^69 + 48*x^68 + 124*x^67 + 112*x^66 + 57*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 22*x^5 + 48*x^4 + 60*x^3 + 112*x^2 + 33*x + 16, x^73 + 60*x^71 + 28*x^70 + 62*x^69 + 100*x^68 + 44*x^67 + 100*x^66 + 97*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 62*x^5 + 36*x^4 + 108*x^3 + 36*x^2 + 73*x + 92, x^73 + 60*x^71 + 88*x^70 + 54*x^69 + 8*x^68 + 60*x^67 + 104*x^66 + 89*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 54*x^5 + 8*x^4 + 124*x^3 + 104*x^2 + 65*x + 56, x^73 + 60*x^71 + 76*x^70 + 94*x^69 + 20*x^68 + 108*x^67 + 116*x^66 + x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 94*x^5 + 84*x^4 + 44*x^3 + 52*x^2 + 105*x + 108, x^73 + 60*x^71 + 72*x^70 + 102*x^69 + 72*x^68 + 28*x^67 + 24*x^66 + 73*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 102*x^5 + 72*x^4 + 92*x^3 + 24*x^2 + 49*x + 88, x^73 + 60*x^71 + 120*x^70 + 118*x^69 + 40*x^68 + 60*x^67 + 72*x^66 + 25*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 118*x^5 + 40*x^4 + 124*x^3 + 72*x^2 + x + 24, x^73 + 60*x^71 + 52*x^70 + 46*x^69 + 92*x^68 + 12*x^67 + 44*x^66 + 17*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 46*x^5 + 28*x^4 + 76*x^3 + 108*x^2 + 121*x + 4, x^73 + 60*x^71 + 44*x^70 + 62*x^69 + 20*x^68 + 44*x^67 + 84*x^66 + 97*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 62*x^5 + 84*x^4 + 108*x^3 + 20*x^2 + 73*x + 44, x^73 + 60*x^71 + 32*x^70 + 86*x^69 + 96*x^68 + 60*x^67 + 96*x^66 + 57*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 86*x^5 + 96*x^4 + 124*x^3 + 96*x^2 + 33*x + 32, x^73 + 60*x^71 + 56*x^70 + 22*x^69 + 104*x^68 + 124*x^67 + 8*x^66 + 57*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 22*x^5 + 104*x^4 + 60*x^3 + 8*x^2 + 33*x + 88, x^73 + 60*x^71 + 12*x^70 + 14*x^69 + 36*x^68 + 76*x^67 + 20*x^66 + 113*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 14*x^5 + 100*x^4 + 12*x^3 + 84*x^2 + 89*x + 124, x^73 + 60*x^71 + 100*x^70 + 46*x^69 + 76*x^68 + 12*x^67 + 60*x^66 + 17*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 46*x^5 + 12*x^4 + 76*x^3 + 124*x^2 + 121*x + 84, x^73 + 60*x^71 + 80*x^70 + 118*x^69 + 48*x^68 + 60*x^67 + 112*x^66 + 25*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 118*x^5 + 48*x^4 + 124*x^3 + 112*x^2 + x + 16, x^73 + 60*x^71 + 4*x^70 + 46*x^69 + 108*x^68 + 76*x^67 + 92*x^66 + 81*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 46*x^5 + 44*x^4 + 12*x^3 + 28*x^2 + 57*x + 116, x^73 + 60*x^71 + 100*x^70 + 46*x^69 + 108*x^68 + 12*x^67 + 124*x^66 + 17*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 46*x^5 + 44*x^4 + 76*x^3 + 60*x^2 + 121*x + 116, x^73 + 60*x^71 + 28*x^70 + 62*x^69 + 68*x^68 + 44*x^67 + 36*x^66 + 97*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 62*x^5 + 4*x^4 + 108*x^3 + 100*x^2 + 73*x + 60, x^73 + 60*x^71 + 32*x^70 + 6*x^69 + 16*x^68 + 28*x^67 + 41*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 6*x^5 + 16*x^4 + 92*x^3 + 17*x + 80, x^73 + 60*x^71 + 16*x^70 + 102*x^69 + 28*x^67 + 16*x^66 + 73*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 102*x^5 + 92*x^3 + 16*x^2 + 49*x + 96, x^73 + 60*x^71 + 68*x^70 + 94*x^69 + 92*x^68 + 108*x^67 + 124*x^66 + x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 94*x^5 + 28*x^4 + 44*x^3 + 60*x^2 + 105*x + 36, x^73 + 60*x^71 + 36*x^70 + 126*x^69 + 124*x^68 + 44*x^67 + 28*x^66 + 33*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 126*x^5 + 60*x^4 + 108*x^3 + 92*x^2 + 9*x + 4, x^73 + 60*x^71 + 4*x^70 + 62*x^69 + 28*x^68 + 44*x^67 + 60*x^66 + 97*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 62*x^5 + 92*x^4 + 108*x^3 + 124*x^2 + 73*x + 100, x^73 + 60*x^71 + 24*x^70 + 70*x^69 + 88*x^68 + 28*x^67 + 72*x^66 + 105*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 70*x^5 + 88*x^4 + 92*x^3 + 72*x^2 + 81*x + 72, x^73 + 60*x^71 + 72*x^70 + 70*x^69 + 40*x^68 + 92*x^67 + 88*x^66 + 41*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 70*x^5 + 40*x^4 + 28*x^3 + 88*x^2 + 17*x + 56, x^73 + 60*x^71 + 104*x^70 + 22*x^69 + 120*x^68 + 60*x^67 + 24*x^66 + 121*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 22*x^5 + 120*x^4 + 124*x^3 + 24*x^2 + 97*x + 8, x^73 + 60*x^71 + 24*x^70 + 102*x^69 + 120*x^68 + 92*x^67 + 8*x^66 + 9*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 102*x^5 + 120*x^4 + 28*x^3 + 8*x^2 + 113*x + 104, x^73 + 60*x^71 + 76*x^70 + 94*x^69 + 116*x^68 + 44*x^67 + 116*x^66 + 65*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 94*x^5 + 52*x^4 + 108*x^3 + 52*x^2 + 41*x + 12, x^73 + 60*x^71 + 24*x^70 + 102*x^69 + 24*x^68 + 92*x^67 + 72*x^66 + 9*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 102*x^5 + 24*x^4 + 28*x^3 + 72*x^2 + 113*x + 8, x^73 + 60*x^71 + 6*x^69 + 112*x^68 + 28*x^67 + 32*x^66 + 41*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 6*x^5 + 112*x^4 + 92*x^3 + 32*x^2 + 17*x + 112, x^73 + 60*x^71 + 24*x^70 + 102*x^69 + 24*x^68 + 28*x^67 + 8*x^66 + 73*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 102*x^5 + 24*x^4 + 92*x^3 + 8*x^2 + 49*x + 72, x^73 + 60*x^71 + 120*x^70 + 22*x^69 + 8*x^68 + 124*x^67 + 8*x^66 + 57*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 22*x^5 + 8*x^4 + 60*x^3 + 8*x^2 + 33*x + 120, x^73 + 60*x^71 + 28*x^70 + 110*x^69 + 116*x^68 + 76*x^67 + 4*x^66 + 17*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 110*x^5 + 52*x^4 + 12*x^3 + 68*x^2 + 121*x + 44, x^73 + 60*x^71 + 124*x^70 + 126*x^69 + 100*x^68 + 108*x^67 + 4*x^66 + 97*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 126*x^5 + 36*x^4 + 44*x^3 + 68*x^2 + 73*x + 92, x^73 + 60*x^71 + 104*x^70 + 70*x^69 + 40*x^68 + 28*x^67 + 56*x^66 + 105*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 70*x^5 + 40*x^4 + 92*x^3 + 56*x^2 + 81*x + 56, x^73 + 60*x^71 + 80*x^70 + 54*x^69 + 48*x^68 + 60*x^67 + 112*x^66 + 89*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 54*x^5 + 48*x^4 + 124*x^3 + 112*x^2 + 65*x + 16, x^73 + 60*x^71 + 64*x^70 + 6*x^69 + 48*x^68 + 28*x^67 + 96*x^66 + 41*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 6*x^5 + 48*x^4 + 92*x^3 + 96*x^2 + 17*x + 48, x^73 + 60*x^71 + 88*x^70 + 86*x^69 + 40*x^68 + 60*x^67 + 104*x^66 + 57*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 86*x^5 + 40*x^4 + 124*x^3 + 104*x^2 + 33*x + 24, x^73 + 60*x^71 + 112*x^70 + 54*x^69 + 16*x^68 + 124*x^67 + 16*x^66 + 25*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 54*x^5 + 16*x^4 + 60*x^3 + 16*x^2 + x + 112, x^73 + 60*x^71 + 72*x^70 + 70*x^69 + 104*x^68 + 92*x^67 + 88*x^66 + 41*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 70*x^5 + 104*x^4 + 28*x^3 + 88*x^2 + 17*x + 120, x^73 + 60*x^71 + 60*x^70 + 62*x^69 + 68*x^68 + 108*x^67 + 4*x^66 + 33*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 62*x^5 + 4*x^4 + 44*x^3 + 68*x^2 + 9*x + 60, x^73 + 60*x^71 + 60*x^70 + 14*x^69 + 52*x^68 + 76*x^67 + 100*x^66 + 113*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 14*x^5 + 116*x^4 + 12*x^3 + 36*x^2 + 89*x + 108, x^73 + 60*x^71 + 44*x^70 + 78*x^69 + 68*x^68 + 76*x^67 + 116*x^66 + 49*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 78*x^5 + 4*x^4 + 12*x^3 + 52*x^2 + 25*x + 92, x^73 + 60*x^71 + 36*x^70 + 62*x^69 + 28*x^68 + 108*x^67 + 28*x^66 + 33*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 62*x^5 + 92*x^4 + 44*x^3 + 92*x^2 + 9*x + 100, x^73 + 60*x^71 + 24*x^70 + 38*x^69 + 88*x^68 + 92*x^67 + 72*x^66 + 73*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 38*x^5 + 88*x^4 + 28*x^3 + 72*x^2 + 49*x + 72, x^73 + 60*x^71 + 104*x^70 + 22*x^69 + 88*x^68 + 124*x^67 + 24*x^66 + 57*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 22*x^5 + 88*x^4 + 60*x^3 + 24*x^2 + 33*x + 40, x^73 + 60*x^71 + 76*x^70 + 110*x^69 + 4*x^68 + 76*x^67 + 84*x^66 + 17*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 110*x^5 + 68*x^4 + 12*x^3 + 20*x^2 + 121*x + 28, x^73 + 60*x^71 + 48*x^70 + 38*x^69 + 32*x^68 + 92*x^67 + 48*x^66 + 73*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 38*x^5 + 32*x^4 + 28*x^3 + 48*x^2 + 49*x, x^73 + 60*x^71 + 8*x^70 + 86*x^69 + 56*x^68 + 60*x^67 + 56*x^66 + 57*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 86*x^5 + 56*x^4 + 124*x^3 + 56*x^2 + 33*x + 8, x^73 + 60*x^71 + 32*x^70 + 6*x^69 + 80*x^68 + 28*x^67 + 41*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 6*x^5 + 80*x^4 + 92*x^3 + 17*x + 16, x^73 + 60*x^71 + 76*x^70 + 78*x^69 + 36*x^68 + 12*x^67 + 20*x^66 + 113*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 78*x^5 + 100*x^4 + 76*x^3 + 84*x^2 + 89*x + 60, x^73 + 60*x^71 + 92*x^70 + 94*x^69 + 100*x^68 + 44*x^67 + 100*x^66 + 65*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 94*x^5 + 36*x^4 + 108*x^3 + 36*x^2 + 41*x + 28, x^73 + 60*x^71 + 20*x^70 + 110*x^69 + 28*x^68 + 76*x^67 + 76*x^66 + 17*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 110*x^5 + 92*x^4 + 12*x^3 + 12*x^2 + 121*x + 68, x^73 + 60*x^71 + 68*x^70 + 94*x^69 + 124*x^68 + 44*x^67 + 124*x^66 + 65*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 94*x^5 + 60*x^4 + 108*x^3 + 60*x^2 + 41*x + 4, x^73 + 60*x^71 + 24*x^70 + 86*x^69 + 72*x^68 + 60*x^67 + 104*x^66 + 57*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 86*x^5 + 72*x^4 + 124*x^3 + 104*x^2 + 33*x + 56, x^73 + 60*x^71 + 52*x^70 + 126*x^69 + 12*x^68 + 108*x^67 + 12*x^66 + 97*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 126*x^5 + 76*x^4 + 44*x^3 + 76*x^2 + 73*x + 116, x^73 + 60*x^71 + 36*x^70 + 126*x^69 + 28*x^68 + 44*x^67 + 92*x^66 + 33*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 126*x^5 + 92*x^4 + 108*x^3 + 28*x^2 + 9*x + 36, x^73 + 60*x^71 + 104*x^70 + 118*x^69 + 88*x^68 + 124*x^67 + 88*x^66 + 89*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 118*x^5 + 88*x^4 + 60*x^3 + 88*x^2 + 65*x + 104, x^73 + 60*x^71 + 68*x^70 + 46*x^69 + 108*x^68 + 12*x^67 + 92*x^66 + 17*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 46*x^5 + 44*x^4 + 76*x^3 + 28*x^2 + 121*x + 52, x^73 + 60*x^71 + 20*x^70 + 30*x^69 + 108*x^68 + 44*x^67 + 44*x^66 + x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 30*x^5 + 44*x^4 + 108*x^3 + 108*x^2 + 105*x + 20, x^73 + 60*x^71 + 44*x^70 + 94*x^69 + 116*x^68 + 44*x^67 + 84*x^66 + 65*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 94*x^5 + 52*x^4 + 108*x^3 + 20*x^2 + 41*x + 76, x^73 + 60*x^71 + 60*x^70 + 110*x^69 + 20*x^68 + 12*x^67 + 36*x^66 + 81*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 110*x^5 + 84*x^4 + 76*x^3 + 100*x^2 + 57*x + 76, x^73 + 60*x^71 + 4*x^70 + 14*x^69 + 108*x^68 + 12*x^67 + 92*x^66 + 49*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 14*x^5 + 44*x^4 + 76*x^3 + 28*x^2 + 25*x + 116, x^73 + 60*x^71 + 4*x^70 + 62*x^69 + 92*x^68 + 44*x^67 + 60*x^66 + 97*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 62*x^5 + 28*x^4 + 108*x^3 + 124*x^2 + 73*x + 36, x^73 + 60*x^71 + 28*x^70 + 14*x^69 + 20*x^68 + 12*x^67 + 68*x^66 + 49*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 14*x^5 + 84*x^4 + 76*x^3 + 4*x^2 + 25*x + 76, x^73 + 60*x^71 + 88*x^70 + 70*x^69 + 56*x^68 + 92*x^67 + 8*x^66 + 41*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 70*x^5 + 56*x^4 + 28*x^3 + 8*x^2 + 17*x + 104, x^73 + 60*x^71 + 124*x^70 + 62*x^69 + 68*x^68 + 44*x^67 + 4*x^66 + 97*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 62*x^5 + 4*x^4 + 108*x^3 + 68*x^2 + 73*x + 124, x^73 + 60*x^71 + 48*x^70 + 70*x^69 + 96*x^68 + 92*x^67 + 112*x^66 + 41*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 70*x^5 + 96*x^4 + 28*x^3 + 112*x^2 + 17*x, x^73 + 60*x^71 + 40*x^70 + 86*x^69 + 56*x^68 + 60*x^67 + 88*x^66 + 57*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 86*x^5 + 56*x^4 + 124*x^3 + 88*x^2 + 33*x + 72, x^73 + 60*x^71 + 64*x^70 + 6*x^69 + 112*x^68 + 92*x^67 + 32*x^66 + 105*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 6*x^5 + 112*x^4 + 28*x^3 + 32*x^2 + 81*x + 48, x^73 + 60*x^71 + 16*x^70 + 86*x^69 + 48*x^68 + 60*x^67 + 112*x^66 + 57*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 86*x^5 + 48*x^4 + 124*x^3 + 112*x^2 + 33*x + 80, x^73 + 60*x^71 + 32*x^70 + 70*x^69 + 48*x^68 + 28*x^67 + 64*x^66 + 105*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 70*x^5 + 48*x^4 + 92*x^3 + 64*x^2 + 81*x + 112, x^73 + 60*x^71 + 56*x^70 + 70*x^69 + 24*x^68 + 92*x^67 + 40*x^66 + 41*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 70*x^5 + 24*x^4 + 28*x^3 + 40*x^2 + 17*x + 8, x^73 + 60*x^71 + 116*x^70 + 78*x^69 + 92*x^68 + 12*x^67 + 44*x^66 + 113*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 78*x^5 + 28*x^4 + 76*x^3 + 108*x^2 + 89*x + 68, x^73 + 60*x^71 + 72*x^70 + 102*x^69 + 72*x^68 + 92*x^67 + 88*x^66 + 9*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 102*x^5 + 72*x^4 + 28*x^3 + 88*x^2 + 113*x + 24, x^73 + 60*x^71 + 44*x^70 + 30*x^69 + 116*x^68 + 44*x^67 + 84*x^66 + x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 30*x^5 + 52*x^4 + 108*x^3 + 20*x^2 + 105*x + 76, x^73 + 60*x^71 + 16*x^70 + 22*x^69 + 48*x^68 + 60*x^67 + 112*x^66 + 121*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 22*x^5 + 48*x^4 + 124*x^3 + 112*x^2 + 97*x + 80, x^73 + 60*x^71 + 76*x^70 + 78*x^69 + 68*x^68 + 12*x^67 + 84*x^66 + 113*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 78*x^5 + 4*x^4 + 76*x^3 + 20*x^2 + 89*x + 92, x^73 + 60*x^71 + 8*x^70 + 22*x^69 + 24*x^68 + 60*x^67 + 120*x^66 + 121*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 22*x^5 + 24*x^4 + 124*x^3 + 120*x^2 + 97*x + 104, x^73 + 60*x^71 + 108*x^70 + 62*x^69 + 20*x^68 + 44*x^67 + 20*x^66 + 97*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 62*x^5 + 84*x^4 + 108*x^3 + 84*x^2 + 73*x + 44, x^73 + 60*x^71 + 112*x^70 + 86*x^69 + 80*x^68 + 124*x^67 + 80*x^66 + 121*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 86*x^5 + 80*x^4 + 60*x^3 + 80*x^2 + 97*x + 112, x^73 + 60*x^71 + 72*x^70 + 86*x^69 + 56*x^68 + 60*x^67 + 120*x^66 + 57*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 86*x^5 + 56*x^4 + 124*x^3 + 120*x^2 + 33*x + 8, x^73 + 60*x^71 + 112*x^70 + 102*x^69 + 92*x^67 + 48*x^66 + 9*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 102*x^5 + 28*x^3 + 48*x^2 + 113*x + 96, x^73 + 60*x^71 + 60*x^70 + 62*x^69 + 68*x^68 + 44*x^67 + 68*x^66 + 97*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 62*x^5 + 4*x^4 + 108*x^3 + 4*x^2 + 73*x + 124, x^73 + 60*x^71 + 40*x^70 + 54*x^69 + 24*x^68 + 60*x^67 + 88*x^66 + 89*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 54*x^5 + 24*x^4 + 124*x^3 + 88*x^2 + 65*x + 104, x^73 + 60*x^71 + 64*x^70 + 54*x^69 + 96*x^68 + 124*x^67 + 25*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 54*x^5 + 96*x^4 + 60*x^3 + x + 96, x^73 + 60*x^71 + 84*x^70 + 94*x^69 + 44*x^68 + 44*x^67 + 108*x^66 + 65*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 94*x^5 + 108*x^4 + 108*x^3 + 44*x^2 + 41*x + 84, x^73 + 60*x^71 + 4*x^70 + 14*x^69 + 12*x^68 + 12*x^67 + 28*x^66 + 49*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 14*x^5 + 76*x^4 + 76*x^3 + 92*x^2 + 25*x + 20, x^73 + 60*x^71 + 124*x^70 + 62*x^69 + 100*x^68 + 108*x^67 + 4*x^66 + 33*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 62*x^5 + 36*x^4 + 44*x^3 + 68*x^2 + 9*x + 92, x^73 + 60*x^71 + 120*x^70 + 118*x^69 + 8*x^68 + 124*x^67 + 72*x^66 + 89*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 118*x^5 + 8*x^4 + 60*x^3 + 72*x^2 + 65*x + 56, x^73 + 60*x^71 + 120*x^70 + 86*x^69 + 104*x^68 + 60*x^67 + 8*x^66 + 57*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 86*x^5 + 104*x^4 + 124*x^3 + 8*x^2 + 33*x + 24, x^73 + 60*x^71 + 52*x^70 + 126*x^69 + 76*x^68 + 108*x^67 + 12*x^66 + 97*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 126*x^5 + 12*x^4 + 44*x^3 + 76*x^2 + 73*x + 52, x^73 + 60*x^71 + 36*x^70 + 94*x^69 + 92*x^68 + 44*x^67 + 28*x^66 + 65*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 94*x^5 + 28*x^4 + 108*x^3 + 92*x^2 + 41*x + 36, x^73 + 60*x^71 + 100*x^70 + 14*x^69 + 44*x^68 + 76*x^67 + 124*x^66 + 113*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 14*x^5 + 108*x^4 + 12*x^3 + 60*x^2 + 89*x + 52, x^73 + 60*x^71 + 12*x^70 + 62*x^69 + 20*x^68 + 108*x^67 + 116*x^66 + 33*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 62*x^5 + 84*x^4 + 44*x^3 + 52*x^2 + 9*x + 44, x^73 + 60*x^71 + 124*x^70 + 46*x^69 + 52*x^68 + 76*x^67 + 100*x^66 + 81*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 46*x^5 + 116*x^4 + 12*x^3 + 36*x^2 + 57*x + 44, x^73 + 60*x^71 + 32*x^70 + 70*x^69 + 112*x^68 + 28*x^67 + 64*x^66 + 105*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 70*x^5 + 112*x^4 + 92*x^3 + 64*x^2 + 81*x + 48, x^73 + 60*x^71 + 48*x^70 + 22*x^69 + 80*x^68 + 124*x^67 + 16*x^66 + 57*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 22*x^5 + 80*x^4 + 60*x^3 + 16*x^2 + 33*x + 112, x^73 + 60*x^71 + 36*x^70 + 30*x^69 + 92*x^68 + 44*x^67 + 28*x^66 + x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 30*x^5 + 28*x^4 + 108*x^3 + 92*x^2 + 105*x + 36, x^73 + 60*x^71 + 40*x^70 + 102*x^69 + 72*x^68 + 92*x^67 + 56*x^66 + 9*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 102*x^5 + 72*x^4 + 28*x^3 + 56*x^2 + 113*x + 88, x^73 + 60*x^71 + 56*x^70 + 86*x^69 + 72*x^68 + 60*x^67 + 8*x^66 + 57*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 86*x^5 + 72*x^4 + 124*x^3 + 8*x^2 + 33*x + 120, x^73 + 60*x^71 + 120*x^70 + 102*x^69 + 120*x^68 + 92*x^67 + 104*x^66 + 9*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 102*x^5 + 120*x^4 + 28*x^3 + 104*x^2 + 113*x + 40, x^73 + 60*x^71 + 8*x^70 + 102*x^69 + 40*x^68 + 28*x^67 + 24*x^66 + 73*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 102*x^5 + 40*x^4 + 92*x^3 + 24*x^2 + 49*x + 56, x^73 + 60*x^71 + 124*x^70 + 46*x^69 + 52*x^68 + 12*x^67 + 36*x^66 + 17*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 46*x^5 + 116*x^4 + 76*x^3 + 100*x^2 + 121*x + 108, x^73 + 60*x^71 + 12*x^70 + 94*x^69 + 84*x^68 + 108*x^67 + 52*x^66 + x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 94*x^5 + 20*x^4 + 44*x^3 + 116*x^2 + 105*x + 44, x^73 + 60*x^71 + 112*x^70 + 102*x^69 + 96*x^68 + 92*x^67 + 112*x^66 + 9*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 102*x^5 + 96*x^4 + 28*x^3 + 112*x^2 + 113*x + 64, x^73 + 60*x^71 + 76*x^70 + 30*x^69 + 84*x^68 + 108*x^67 + 116*x^66 + 65*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 30*x^5 + 20*x^4 + 44*x^3 + 52*x^2 + 41*x + 44, x^73 + 60*x^71 + 116*x^70 + 14*x^69 + 28*x^68 + 12*x^67 + 44*x^66 + 49*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 14*x^5 + 92*x^4 + 76*x^3 + 108*x^2 + 25*x + 4, x^73 + 60*x^71 + 16*x^70 + 118*x^69 + 16*x^68 + 60*x^67 + 112*x^66 + 25*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 118*x^5 + 16*x^4 + 124*x^3 + 112*x^2 + x + 112, x^73 + 60*x^71 + 20*x^70 + 78*x^69 + 92*x^68 + 76*x^67 + 12*x^66 + 49*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 78*x^5 + 28*x^4 + 12*x^3 + 76*x^2 + 25*x + 68, x^73 + 60*x^71 + 68*x^70 + 78*x^69 + 12*x^68 + 12*x^67 + 92*x^66 + 113*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 78*x^5 + 76*x^4 + 76*x^3 + 28*x^2 + 89*x + 20, x^73 + 60*x^71 + 24*x^70 + 86*x^69 + 72*x^68 + 124*x^67 + 40*x^66 + 121*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 86*x^5 + 72*x^4 + 60*x^3 + 40*x^2 + 97*x + 120, x^73 + 60*x^71 + 70*x^69 + 16*x^68 + 92*x^67 + 32*x^66 + 41*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 70*x^5 + 16*x^4 + 28*x^3 + 32*x^2 + 17*x + 80, x^73 + 60*x^71 + 72*x^70 + 54*x^69 + 24*x^68 + 124*x^67 + 56*x^66 + 25*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 54*x^5 + 24*x^4 + 60*x^3 + 56*x^2 + x + 104, x^73 + 60*x^71 + 76*x^70 + 126*x^69 + 84*x^68 + 108*x^67 + 52*x^66 + 97*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 126*x^5 + 20*x^4 + 44*x^3 + 116*x^2 + 73*x + 108, x^73 + 60*x^71 + 36*x^70 + 94*x^69 + 60*x^68 + 108*x^67 + 28*x^66 + x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 94*x^5 + 124*x^4 + 44*x^3 + 92*x^2 + 105*x + 68, x^73 + 60*x^71 + 80*x^70 + 38*x^69 + 32*x^68 + 28*x^67 + 16*x^66 + 9*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 38*x^5 + 32*x^4 + 92*x^3 + 16*x^2 + 113*x, x^73 + 60*x^71 + 124*x^70 + 94*x^69 + 36*x^68 + 44*x^67 + 4*x^66 + 65*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 94*x^5 + 100*x^4 + 108*x^3 + 68*x^2 + 41*x + 28, x^73 + 60*x^71 + 16*x^70 + 54*x^69 + 80*x^68 + 60*x^67 + 112*x^66 + 89*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 54*x^5 + 80*x^4 + 124*x^3 + 112*x^2 + 65*x + 48, x^73 + 60*x^71 + 28*x^70 + 126*x^69 + 68*x^68 + 108*x^67 + 100*x^66 + 97*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 126*x^5 + 4*x^4 + 44*x^3 + 36*x^2 + 73*x + 124, x^73 + 60*x^71 + 56*x^70 + 22*x^69 + 40*x^68 + 124*x^67 + 8*x^66 + 57*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 22*x^5 + 40*x^4 + 60*x^3 + 8*x^2 + 33*x + 24, x^73 + 60*x^71 + 32*x^70 + 6*x^69 + 16*x^68 + 92*x^67 + 64*x^66 + 105*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 6*x^5 + 16*x^4 + 28*x^3 + 64*x^2 + 81*x + 16, x^73 + 60*x^71 + 88*x^70 + 118*x^69 + 72*x^68 + 124*x^67 + 40*x^66 + 89*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 118*x^5 + 72*x^4 + 60*x^3 + 40*x^2 + 65*x + 56, x^73 + 60*x^71 + 118*x^69 + 32*x^68 + 124*x^67 + 64*x^66 + 89*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 118*x^5 + 32*x^4 + 60*x^3 + 64*x^2 + 65*x + 32, x^73 + 60*x^71 + 104*x^70 + 118*x^69 + 24*x^68 + 60*x^67 + 24*x^66 + 25*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 118*x^5 + 24*x^4 + 124*x^3 + 24*x^2 + x + 104, x^73 + 60*x^71 + 104*x^70 + 118*x^69 + 120*x^68 + 124*x^67 + 24*x^66 + 89*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 118*x^5 + 120*x^4 + 60*x^3 + 24*x^2 + 65*x + 8, x^73 + 60*x^71 + 24*x^70 + 70*x^69 + 120*x^68 + 28*x^67 + 8*x^66 + 105*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 70*x^5 + 120*x^4 + 92*x^3 + 8*x^2 + 81*x + 104, x^73 + 60*x^71 + 8*x^70 + 86*x^69 + 56*x^68 + 124*x^67 + 120*x^66 + 121*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 86*x^5 + 56*x^4 + 60*x^3 + 120*x^2 + 97*x + 72, x^73 + 60*x^71 + 60*x^70 + 110*x^69 + 52*x^68 + 76*x^67 + 36*x^66 + 17*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 110*x^5 + 116*x^4 + 12*x^3 + 100*x^2 + 121*x + 44, x^73 + 60*x^71 + 88*x^70 + 38*x^69 + 24*x^68 + 28*x^67 + 72*x^66 + 9*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 38*x^5 + 24*x^4 + 92*x^3 + 72*x^2 + 113*x + 72, x^73 + 60*x^71 + 28*x^70 + 110*x^69 + 84*x^68 + 76*x^67 + 68*x^66 + 17*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 110*x^5 + 20*x^4 + 12*x^3 + 4*x^2 + 121*x + 12, x^73 + 60*x^71 + 32*x^70 + 70*x^69 + 112*x^68 + 92*x^67 + 41*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 70*x^5 + 112*x^4 + 28*x^3 + 17*x + 112, x^73 + 60*x^71 + 40*x^70 + 54*x^69 + 120*x^68 + 60*x^67 + 24*x^66 + 89*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 54*x^5 + 120*x^4 + 124*x^3 + 24*x^2 + 65*x + 72, x^73 + 60*x^71 + 8*x^70 + 6*x^69 + 72*x^68 + 92*x^67 + 88*x^66 + 105*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 6*x^5 + 72*x^4 + 28*x^3 + 88*x^2 + 81*x + 88, x^73 + 60*x^71 + 88*x^70 + 70*x^69 + 56*x^68 + 28*x^67 + 72*x^66 + 105*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 70*x^5 + 56*x^4 + 92*x^3 + 72*x^2 + 81*x + 40, x^73 + 60*x^71 + 52*x^70 + 110*x^69 + 60*x^68 + 76*x^67 + 44*x^66 + 17*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 110*x^5 + 124*x^4 + 12*x^3 + 108*x^2 + 121*x + 36, x^73 + 60*x^71 + 4*x^70 + 62*x^69 + 124*x^68 + 44*x^67 + 124*x^66 + 97*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 62*x^5 + 60*x^4 + 108*x^3 + 60*x^2 + 73*x + 68, x^73 + 60*x^71 + 100*x^70 + 30*x^69 + 124*x^68 + 108*x^67 + 92*x^66 + 65*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 30*x^5 + 60*x^4 + 44*x^3 + 28*x^2 + 41*x + 4, x^73 + 60*x^71 + 84*x^70 + 14*x^69 + 92*x^68 + 12*x^67 + 12*x^66 + 49*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 14*x^5 + 28*x^4 + 76*x^3 + 76*x^2 + 25*x + 4, x^73 + 60*x^71 + 124*x^70 + 30*x^69 + 36*x^68 + 108*x^67 + 68*x^66 + 65*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 30*x^5 + 100*x^4 + 44*x^3 + 4*x^2 + 41*x + 92, x^73 + 60*x^71 + 108*x^70 + 94*x^69 + 84*x^68 + 108*x^67 + 20*x^66 + x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 94*x^5 + 20*x^4 + 44*x^3 + 84*x^2 + 105*x + 108, x^73 + 60*x^71 + 96*x^70 + 22*x^69 + 32*x^68 + 60*x^67 + 32*x^66 + 121*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 22*x^5 + 32*x^4 + 124*x^3 + 32*x^2 + 97*x + 96, x^73 + 60*x^71 + 68*x^70 + 46*x^69 + 108*x^68 + 76*x^67 + 28*x^66 + 81*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 46*x^5 + 44*x^4 + 12*x^3 + 92*x^2 + 57*x + 116, x^73 + 60*x^71 + 70*x^69 + 80*x^68 + 92*x^67 + 32*x^66 + 41*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 70*x^5 + 80*x^4 + 28*x^3 + 32*x^2 + 17*x + 16, x^73 + 60*x^71 + 76*x^70 + 94*x^69 + 84*x^68 + 44*x^67 + 52*x^66 + 65*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 94*x^5 + 20*x^4 + 108*x^3 + 116*x^2 + 41*x + 108, x^73 + 60*x^71 + 36*x^70 + 78*x^69 + 76*x^68 + 12*x^67 + 60*x^66 + 113*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 78*x^5 + 12*x^4 + 76*x^3 + 124*x^2 + 89*x + 20, x^73 + 60*x^71 + 16*x^70 + 54*x^69 + 48*x^68 + 60*x^67 + 48*x^66 + 89*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 54*x^5 + 48*x^4 + 124*x^3 + 48*x^2 + 65*x + 16, x^73 + 60*x^71 + 48*x^70 + 6*x^69 + 96*x^68 + 92*x^67 + 112*x^66 + 105*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 6*x^5 + 96*x^4 + 28*x^3 + 112*x^2 + 81*x, x^73 + 60*x^71 + 16*x^70 + 22*x^69 + 80*x^68 + 60*x^67 + 48*x^66 + 121*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 22*x^5 + 80*x^4 + 124*x^3 + 48*x^2 + 97*x + 112, x^73 + 60*x^71 + 24*x^70 + 86*x^69 + 104*x^68 + 60*x^67 + 40*x^66 + 57*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 86*x^5 + 104*x^4 + 124*x^3 + 40*x^2 + 33*x + 88, x^73 + 60*x^71 + 104*x^70 + 22*x^69 + 24*x^68 + 60*x^67 + 88*x^66 + 121*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 22*x^5 + 24*x^4 + 124*x^3 + 88*x^2 + 97*x + 40, x^73 + 60*x^71 + 104*x^70 + 22*x^69 + 56*x^68 + 124*x^67 + 88*x^66 + 57*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 22*x^5 + 56*x^4 + 60*x^3 + 88*x^2 + 33*x + 8, x^73 + 60*x^71 + 56*x^70 + 6*x^69 + 120*x^68 + 92*x^67 + 104*x^66 + 105*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 6*x^5 + 120*x^4 + 28*x^3 + 104*x^2 + 81*x + 104, x^73 + 60*x^71 + 80*x^70 + 102*x^69 + 28*x^67 + 80*x^66 + 73*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 104*x^35 + 96*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 102*x^5 + 92*x^3 + 80*x^2 + 49*x + 96, x^73 + 60*x^71 + 32*x^70 + 22*x^69 + 96*x^68 + 124*x^67 + 32*x^66 + 57*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 22*x^5 + 96*x^4 + 60*x^3 + 32*x^2 + 33*x + 96, x^73 + 60*x^71 + 60*x^70 + 94*x^69 + 36*x^68 + 44*x^67 + 68*x^66 + 65*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 94*x^5 + 100*x^4 + 108*x^3 + 4*x^2 + 41*x + 28, x^73 + 60*x^71 + 64*x^70 + 70*x^69 + 16*x^68 + 28*x^67 + 32*x^66 + 105*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 70*x^5 + 16*x^4 + 92*x^3 + 32*x^2 + 81*x + 16, x^73 + 60*x^71 + 64*x^70 + 54*x^69 + 32*x^68 + 124*x^67 + 25*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 54*x^5 + 32*x^4 + 60*x^3 + x + 32, x^73 + 60*x^71 + 120*x^70 + 86*x^69 + 72*x^68 + 124*x^67 + 8*x^66 + 121*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 86*x^5 + 72*x^4 + 60*x^3 + 8*x^2 + 97*x + 56, x^73 + 60*x^71 + 8*x^70 + 22*x^69 + 120*x^68 + 124*x^67 + 120*x^66 + 57*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 22*x^5 + 120*x^4 + 60*x^3 + 120*x^2 + 33*x + 8, x^73 + 60*x^71 + 84*x^70 + 126*x^69 + 12*x^68 + 108*x^67 + 44*x^66 + 97*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 126*x^5 + 76*x^4 + 44*x^3 + 108*x^2 + 73*x + 52, x^73 + 60*x^71 + 32*x^70 + 118*x^69 + 60*x^67 + 96*x^66 + 25*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 118*x^5 + 124*x^3 + 96*x^2 + x, x^73 + 60*x^71 + 40*x^70 + 54*x^69 + 24*x^68 + 124*x^67 + 24*x^66 + 25*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 54*x^5 + 24*x^4 + 60*x^3 + 24*x^2 + x + 40, x^73 + 60*x^71 + 100*x^70 + 62*x^69 + 60*x^68 + 44*x^67 + 92*x^66 + 97*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 62*x^5 + 124*x^4 + 108*x^3 + 28*x^2 + 73*x + 68, x^73 + 60*x^71 + 44*x^70 + 46*x^69 + 100*x^68 + 76*x^67 + 116*x^66 + 81*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 46*x^5 + 36*x^4 + 12*x^3 + 52*x^2 + 57*x + 60, x^73 + 60*x^71 + 4*x^70 + 14*x^69 + 44*x^68 + 12*x^67 + 92*x^66 + 49*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 14*x^5 + 108*x^4 + 76*x^3 + 28*x^2 + 25*x + 52, x^73 + 60*x^71 + 80*x^70 + 86*x^69 + 112*x^68 + 124*x^67 + 112*x^66 + 121*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 86*x^5 + 112*x^4 + 60*x^3 + 112*x^2 + 97*x + 80, x^73 + 60*x^71 + 92*x^70 + 14*x^69 + 116*x^68 + 12*x^67 + 68*x^66 + 49*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 14*x^5 + 52*x^4 + 76*x^3 + 4*x^2 + 25*x + 44, x^73 + 60*x^71 + 32*x^70 + 6*x^69 + 48*x^68 + 92*x^67 + 105*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 6*x^5 + 48*x^4 + 28*x^3 + 81*x + 48, x^73 + 60*x^71 + 84*x^70 + 94*x^69 + 76*x^68 + 44*x^67 + 44*x^66 + 65*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 94*x^5 + 12*x^4 + 108*x^3 + 108*x^2 + 41*x + 116, x^73 + 60*x^71 + 16*x^70 + 70*x^69 + 32*x^68 + 28*x^67 + 16*x^66 + 105*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 70*x^5 + 32*x^4 + 92*x^3 + 16*x^2 + 81*x + 64, x^73 + 60*x^71 + 56*x^70 + 6*x^69 + 88*x^68 + 28*x^67 + 104*x^66 + 41*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 6*x^5 + 88*x^4 + 92*x^3 + 104*x^2 + 17*x + 8, x^73 + 60*x^71 + 16*x^70 + 54*x^69 + 80*x^68 + 124*x^67 + 48*x^66 + 25*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 54*x^5 + 80*x^4 + 60*x^3 + 48*x^2 + x + 112, x^73 + 60*x^71 + 8*x^70 + 86*x^69 + 88*x^68 + 124*x^67 + 56*x^66 + 121*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 86*x^5 + 88*x^4 + 60*x^3 + 56*x^2 + 97*x + 104, x^73 + 60*x^71 + 36*x^70 + 126*x^69 + 124*x^68 + 108*x^67 + 92*x^66 + 97*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 126*x^5 + 60*x^4 + 44*x^3 + 28*x^2 + 73*x + 68, x^73 + 60*x^71 + 124*x^70 + 62*x^69 + 68*x^68 + 108*x^67 + 68*x^66 + 33*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 62*x^5 + 4*x^4 + 44*x^3 + 4*x^2 + 9*x + 60, x^73 + 60*x^71 + 120*x^70 + 118*x^69 + 72*x^68 + 124*x^67 + 72*x^66 + 89*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 118*x^5 + 72*x^4 + 60*x^3 + 72*x^2 + 65*x + 120, x^73 + 60*x^71 + 124*x^70 + 14*x^69 + 52*x^68 + 12*x^67 + 100*x^66 + 49*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 14*x^5 + 116*x^4 + 76*x^3 + 36*x^2 + 25*x + 44, x^73 + 60*x^71 + 8*x^70 + 38*x^69 + 40*x^68 + 92*x^67 + 88*x^66 + 73*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 38*x^5 + 40*x^4 + 28*x^3 + 88*x^2 + 49*x + 120, x^73 + 60*x^71 + 76*x^70 + 110*x^69 + 68*x^68 + 12*x^67 + 20*x^66 + 81*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 110*x^5 + 4*x^4 + 76*x^3 + 84*x^2 + 57*x + 28, x^73 + 60*x^71 + 20*x^70 + 30*x^69 + 76*x^68 + 44*x^67 + 108*x^66 + x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 30*x^5 + 12*x^4 + 108*x^3 + 44*x^2 + 105*x + 116, x^73 + 60*x^71 + 76*x^70 + 62*x^69 + 20*x^68 + 44*x^67 + 116*x^66 + 97*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 62*x^5 + 84*x^4 + 108*x^3 + 52*x^2 + 73*x + 108, x^73 + 60*x^71 + 28*x^70 + 94*x^69 + 100*x^68 + 44*x^67 + 36*x^66 + 65*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 94*x^5 + 36*x^4 + 108*x^3 + 100*x^2 + 41*x + 28, x^73 + 60*x^71 + 84*x^70 + 110*x^69 + 92*x^68 + 12*x^67 + 76*x^66 + 81*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 110*x^5 + 28*x^4 + 76*x^3 + 12*x^2 + 57*x + 68, x^73 + 60*x^71 + 60*x^70 + 126*x^69 + 4*x^68 + 108*x^67 + 4*x^66 + 97*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 126*x^5 + 68*x^4 + 44*x^3 + 68*x^2 + 73*x + 124, x^73 + 60*x^71 + 64*x^70 + 54*x^69 + 124*x^67 + 64*x^66 + 25*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 54*x^5 + 60*x^3 + 64*x^2 + x, x^73 + 60*x^71 + 20*x^70 + 78*x^69 + 124*x^68 + 76*x^67 + 76*x^66 + 49*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 78*x^5 + 60*x^4 + 12*x^3 + 12*x^2 + 25*x + 100, x^73 + 60*x^71 + 20*x^70 + 78*x^69 + 92*x^68 + 12*x^67 + 76*x^66 + 113*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 78*x^5 + 28*x^4 + 76*x^3 + 12*x^2 + 89*x + 4, x^73 + 60*x^71 + 124*x^70 + 78*x^69 + 116*x^68 + 76*x^67 + 36*x^66 + 49*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 78*x^5 + 52*x^4 + 12*x^3 + 100*x^2 + 25*x + 44, x^73 + 60*x^71 + 24*x^70 + 118*x^69 + 8*x^68 + 124*x^67 + 104*x^66 + 89*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 118*x^5 + 8*x^4 + 60*x^3 + 104*x^2 + 65*x + 120, x^73 + 60*x^71 + 12*x^70 + 78*x^69 + 68*x^68 + 12*x^67 + 20*x^66 + 113*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 78*x^5 + 4*x^4 + 76*x^3 + 84*x^2 + 89*x + 92, x^73 + 60*x^71 + 100*x^70 + 62*x^69 + 60*x^68 + 108*x^67 + 28*x^66 + 33*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 62*x^5 + 124*x^4 + 44*x^3 + 92*x^2 + 9*x + 4, x^73 + 60*x^71 + 100*x^70 + 126*x^69 + 28*x^68 + 108*x^67 + 92*x^66 + 97*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 126*x^5 + 92*x^4 + 44*x^3 + 28*x^2 + 73*x + 100, x^73 + 60*x^71 + 104*x^70 + 86*x^69 + 24*x^68 + 124*x^67 + 24*x^66 + 121*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 86*x^5 + 24*x^4 + 60*x^3 + 24*x^2 + 97*x + 104, x^73 + 60*x^71 + 108*x^70 + 94*x^69 + 52*x^68 + 108*x^67 + 84*x^66 + x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 94*x^5 + 116*x^4 + 44*x^3 + 20*x^2 + 105*x + 76, x^73 + 60*x^71 + 92*x^70 + 78*x^69 + 52*x^68 + 12*x^67 + 68*x^66 + 113*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 78*x^5 + 116*x^4 + 76*x^3 + 4*x^2 + 89*x + 108, x^73 + 60*x^71 + 70*x^69 + 48*x^68 + 28*x^67 + 32*x^66 + 105*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 70*x^5 + 48*x^4 + 92*x^3 + 32*x^2 + 81*x + 48, x^73 + 60*x^71 + 68*x^70 + 62*x^69 + 92*x^68 + 44*x^67 + 124*x^66 + 97*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 62*x^5 + 28*x^4 + 108*x^3 + 60*x^2 + 73*x + 36, x^73 + 60*x^71 + 120*x^70 + 38*x^69 + 24*x^68 + 28*x^67 + 104*x^66 + 9*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 38*x^5 + 24*x^4 + 92*x^3 + 104*x^2 + 113*x + 8, x^73 + 60*x^71 + 108*x^70 + 14*x^69 + 36*x^68 + 76*x^67 + 116*x^66 + 113*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 14*x^5 + 100*x^4 + 12*x^3 + 52*x^2 + 89*x + 60, x^73 + 60*x^71 + 84*x^70 + 46*x^69 + 92*x^68 + 76*x^67 + 12*x^66 + 81*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 46*x^5 + 28*x^4 + 12*x^3 + 76*x^2 + 57*x + 4, x^73 + 60*x^71 + 60*x^70 + 110*x^69 + 20*x^68 + 76*x^67 + 100*x^66 + 17*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 110*x^5 + 84*x^4 + 12*x^3 + 36*x^2 + 121*x + 12, x^73 + 60*x^71 + 20*x^70 + 110*x^69 + 60*x^68 + 76*x^67 + 12*x^66 + 17*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 110*x^5 + 124*x^4 + 12*x^3 + 76*x^2 + 121*x + 100, x^73 + 60*x^71 + 40*x^70 + 86*x^69 + 56*x^68 + 124*x^67 + 24*x^66 + 121*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 86*x^5 + 56*x^4 + 60*x^3 + 24*x^2 + 97*x + 8, x^73 + 60*x^71 + 20*x^70 + 46*x^69 + 124*x^68 + 76*x^67 + 12*x^66 + 81*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 46*x^5 + 60*x^4 + 12*x^3 + 76*x^2 + 57*x + 36, x^73 + 60*x^71 + 68*x^70 + 126*x^69 + 124*x^68 + 44*x^67 + 60*x^66 + 33*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 126*x^5 + 60*x^4 + 108*x^3 + 124*x^2 + 9*x + 68, x^73 + 60*x^71 + 100*x^70 + 126*x^69 + 60*x^68 + 108*x^67 + 28*x^66 + 97*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 126*x^5 + 124*x^4 + 44*x^3 + 92*x^2 + 73*x + 4, x^73 + 60*x^71 + 116*x^70 + 110*x^69 + 92*x^68 + 12*x^67 + 108*x^66 + 81*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 110*x^5 + 28*x^4 + 76*x^3 + 44*x^2 + 57*x + 4, x^73 + 60*x^71 + 16*x^70 + 6*x^69 + 32*x^68 + 28*x^67 + 16*x^66 + 41*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 6*x^5 + 32*x^4 + 92*x^3 + 16*x^2 + 17*x + 64, x^73 + 60*x^71 + 88*x^70 + 70*x^69 + 88*x^68 + 28*x^67 + 8*x^66 + 105*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 70*x^5 + 88*x^4 + 92*x^3 + 8*x^2 + 81*x + 72, x^73 + 60*x^71 + 56*x^70 + 102*x^69 + 88*x^68 + 92*x^67 + 104*x^66 + 9*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 102*x^5 + 88*x^4 + 28*x^3 + 104*x^2 + 113*x + 8, x^73 + 60*x^71 + 120*x^70 + 70*x^69 + 120*x^68 + 28*x^67 + 104*x^66 + 105*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 70*x^5 + 120*x^4 + 92*x^3 + 104*x^2 + 81*x + 40, x^73 + 60*x^71 + 36*x^70 + 94*x^69 + 92*x^68 + 108*x^67 + 92*x^66 + x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 94*x^5 + 28*x^4 + 44*x^3 + 28*x^2 + 105*x + 100, x^73 + 60*x^71 + 4*x^70 + 94*x^69 + 92*x^68 + 44*x^67 + 124*x^66 + 65*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 94*x^5 + 28*x^4 + 108*x^3 + 60*x^2 + 41*x + 100, x^73 + 60*x^71 + 68*x^70 + 78*x^69 + 76*x^68 + 76*x^67 + 28*x^66 + 49*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 78*x^5 + 12*x^4 + 12*x^3 + 92*x^2 + 25*x + 20, x^73 + 60*x^71 + 16*x^70 + 6*x^69 + 28*x^67 + 80*x^66 + 41*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 6*x^5 + 92*x^3 + 80*x^2 + 17*x + 32, x^73 + 60*x^71 + 76*x^70 + 78*x^69 + 100*x^68 + 12*x^67 + 20*x^66 + 113*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 78*x^5 + 36*x^4 + 76*x^3 + 84*x^2 + 89*x + 124, x^73 + 60*x^71 + 48*x^70 + 86*x^69 + 112*x^68 + 60*x^67 + 16*x^66 + 57*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 86*x^5 + 112*x^4 + 124*x^3 + 16*x^2 + 33*x + 80, x^73 + 60*x^71 + 28*x^70 + 94*x^69 + 68*x^68 + 108*x^67 + 36*x^66 + x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 94*x^5 + 4*x^4 + 44*x^3 + 100*x^2 + 105*x + 60, x^73 + 60*x^71 + 36*x^70 + 62*x^69 + 60*x^68 + 108*x^67 + 92*x^66 + 33*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 62*x^5 + 124*x^4 + 44*x^3 + 28*x^2 + 9*x + 4, x^73 + 60*x^71 + 64*x^70 + 22*x^69 + 60*x^67 + 64*x^66 + 121*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 22*x^5 + 124*x^3 + 64*x^2 + 97*x, x^73 + 60*x^71 + 4*x^70 + 126*x^69 + 124*x^68 + 44*x^67 + 124*x^66 + 33*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 126*x^5 + 60*x^4 + 108*x^3 + 60*x^2 + 9*x + 68, x^73 + 60*x^71 + 32*x^70 + 6*x^69 + 80*x^68 + 92*x^67 + 64*x^66 + 105*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 6*x^5 + 80*x^4 + 28*x^3 + 64*x^2 + 81*x + 80, x^73 + 60*x^71 + 72*x^70 + 38*x^69 + 104*x^68 + 28*x^67 + 88*x^66 + 9*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 38*x^5 + 104*x^4 + 92*x^3 + 88*x^2 + 113*x + 120, x^73 + 60*x^71 + 56*x^70 + 118*x^69 + 40*x^68 + 124*x^67 + 72*x^66 + 89*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 118*x^5 + 40*x^4 + 60*x^3 + 72*x^2 + 65*x + 88, x^73 + 60*x^71 + 88*x^70 + 86*x^69 + 40*x^68 + 124*x^67 + 40*x^66 + 121*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 86*x^5 + 40*x^4 + 60*x^3 + 40*x^2 + 97*x + 88, x^73 + 60*x^71 + 120*x^70 + 38*x^69 + 88*x^68 + 92*x^67 + 40*x^66 + 73*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 38*x^5 + 88*x^4 + 28*x^3 + 40*x^2 + 49*x + 8, x^73 + 60*x^71 + 64*x^70 + 38*x^69 + 16*x^68 + 92*x^67 + 32*x^66 + 73*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 38*x^5 + 16*x^4 + 28*x^3 + 32*x^2 + 49*x + 16, x^73 + 60*x^71 + 80*x^70 + 22*x^69 + 16*x^68 + 124*x^67 + 48*x^66 + 57*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 22*x^5 + 16*x^4 + 60*x^3 + 48*x^2 + 33*x + 112, x^73 + 60*x^71 + 116*x^70 + 62*x^69 + 12*x^68 + 108*x^67 + 76*x^66 + 33*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 62*x^5 + 76*x^4 + 44*x^3 + 12*x^2 + 9*x + 116, x^73 + 60*x^71 + 96*x^70 + 22*x^69 + 96*x^68 + 124*x^67 + 96*x^66 + 57*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 22*x^5 + 96*x^4 + 60*x^3 + 96*x^2 + 33*x + 96, x^73 + 60*x^71 + 68*x^70 + 46*x^69 + 76*x^68 + 76*x^67 + 92*x^66 + 81*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 46*x^5 + 12*x^4 + 12*x^3 + 28*x^2 + 57*x + 84, x^73 + 60*x^71 + 124*x^70 + 46*x^69 + 116*x^68 + 76*x^67 + 100*x^66 + 81*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 46*x^5 + 52*x^4 + 12*x^3 + 36*x^2 + 57*x + 108, x^73 + 60*x^71 + 104*x^70 + 22*x^69 + 56*x^68 + 60*x^67 + 24*x^66 + 121*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 22*x^5 + 56*x^4 + 124*x^3 + 24*x^2 + 97*x + 72, x^73 + 60*x^71 + 96*x^70 + 54*x^69 + 64*x^68 + 124*x^67 + 96*x^66 + 25*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 54*x^5 + 64*x^4 + 60*x^3 + 96*x^2 + x, x^73 + 60*x^71 + 116*x^70 + 30*x^69 + 76*x^68 + 44*x^67 + 76*x^66 + x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 30*x^5 + 12*x^4 + 108*x^3 + 12*x^2 + 105*x + 52, x^73 + 60*x^71 + 108*x^70 + 14*x^69 + 68*x^68 + 12*x^67 + 116*x^66 + 49*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 14*x^5 + 4*x^4 + 76*x^3 + 52*x^2 + 25*x + 28, x^73 + 60*x^71 + 24*x^70 + 54*x^69 + 8*x^68 + 60*x^67 + 40*x^66 + 89*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 54*x^5 + 8*x^4 + 124*x^3 + 40*x^2 + 65*x + 56, x^73 + 60*x^71 + 12*x^70 + 78*x^69 + 68*x^68 + 76*x^67 + 84*x^66 + 49*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 78*x^5 + 4*x^4 + 12*x^3 + 20*x^2 + 25*x + 28, x^73 + 60*x^71 + 4*x^70 + 126*x^69 + 60*x^68 + 108*x^67 + 60*x^66 + 97*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 126*x^5 + 124*x^4 + 44*x^3 + 124*x^2 + 73*x + 68, x^73 + 60*x^71 + 76*x^70 + 94*x^69 + 52*x^68 + 108*x^67 + 52*x^66 + x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 94*x^5 + 116*x^4 + 44*x^3 + 116*x^2 + 105*x + 12, x^73 + 60*x^71 + 44*x^70 + 30*x^69 + 20*x^68 + 44*x^67 + 20*x^66 + x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 30*x^5 + 84*x^4 + 108*x^3 + 84*x^2 + 105*x + 108, x^73 + 60*x^71 + 40*x^70 + 6*x^69 + 40*x^68 + 28*x^67 + 120*x^66 + 41*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 6*x^5 + 40*x^4 + 92*x^3 + 120*x^2 + 17*x + 56, x^73 + 60*x^71 + 116*x^70 + 126*x^69 + 76*x^68 + 44*x^67 + 12*x^66 + 33*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 126*x^5 + 12*x^4 + 108*x^3 + 76*x^2 + 9*x + 116, x^73 + 60*x^71 + 48*x^70 + 118*x^69 + 80*x^68 + 60*x^67 + 16*x^66 + 25*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 118*x^5 + 80*x^4 + 124*x^3 + 16*x^2 + x + 112, x^73 + 60*x^71 + 76*x^70 + 30*x^69 + 84*x^68 + 44*x^67 + 52*x^66 + x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 30*x^5 + 20*x^4 + 108*x^3 + 116*x^2 + 105*x + 108, x^73 + 60*x^71 + 52*x^70 + 126*x^69 + 44*x^68 + 108*x^67 + 76*x^66 + 97*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 126*x^5 + 108*x^4 + 44*x^3 + 12*x^2 + 73*x + 20, x^73 + 60*x^71 + 96*x^70 + 118*x^69 + 96*x^68 + 60*x^67 + 96*x^66 + 25*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 118*x^5 + 96*x^4 + 124*x^3 + 96*x^2 + x + 96, x^73 + 60*x^71 + 116*x^70 + 110*x^69 + 60*x^68 + 76*x^67 + 108*x^66 + 17*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 110*x^5 + 124*x^4 + 12*x^3 + 44*x^2 + 121*x + 36, x^73 + 60*x^71 + 24*x^70 + 102*x^69 + 56*x^68 + 92*x^67 + 8*x^66 + 9*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 102*x^5 + 56*x^4 + 28*x^3 + 8*x^2 + 113*x + 40, x^73 + 60*x^71 + 80*x^70 + 54*x^69 + 80*x^68 + 60*x^67 + 48*x^66 + 89*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 54*x^5 + 80*x^4 + 124*x^3 + 48*x^2 + 65*x + 48, x^73 + 60*x^71 + 80*x^70 + 70*x^69 + 96*x^68 + 28*x^67 + 80*x^66 + 105*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 70*x^5 + 96*x^4 + 92*x^3 + 80*x^2 + 81*x, x^73 + 60*x^71 + 124*x^70 + 30*x^69 + 100*x^68 + 44*x^67 + 4*x^66 + x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 30*x^5 + 36*x^4 + 108*x^3 + 68*x^2 + 105*x + 92, x^73 + 60*x^71 + 44*x^70 + 14*x^69 + 36*x^68 + 12*x^67 + 116*x^66 + 49*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 14*x^5 + 100*x^4 + 76*x^3 + 52*x^2 + 25*x + 124, x^73 + 60*x^71 + 64*x^70 + 70*x^69 + 80*x^68 + 28*x^67 + 32*x^66 + 105*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 70*x^5 + 80*x^4 + 92*x^3 + 32*x^2 + 81*x + 80, x^73 + 60*x^71 + 96*x^70 + 6*x^69 + 16*x^68 + 28*x^67 + 64*x^66 + 41*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 6*x^5 + 16*x^4 + 92*x^3 + 64*x^2 + 17*x + 80, x^73 + 60*x^71 + 100*x^70 + 62*x^69 + 28*x^68 + 44*x^67 + 28*x^66 + 97*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 62*x^5 + 92*x^4 + 108*x^3 + 92*x^2 + 73*x + 36, x^73 + 60*x^71 + 24*x^70 + 86*x^69 + 40*x^68 + 60*x^67 + 40*x^66 + 57*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 86*x^5 + 40*x^4 + 124*x^3 + 40*x^2 + 33*x + 24, x^73 + 60*x^71 + 88*x^70 + 6*x^69 + 120*x^68 + 28*x^67 + 72*x^66 + 41*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 6*x^5 + 120*x^4 + 92*x^3 + 72*x^2 + 17*x + 104, x^73 + 60*x^71 + 12*x^70 + 110*x^69 + 100*x^68 + 12*x^67 + 20*x^66 + 81*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 110*x^5 + 36*x^4 + 76*x^3 + 84*x^2 + 57*x + 60, x^73 + 60*x^71 + 44*x^70 + 94*x^69 + 52*x^68 + 108*x^67 + 20*x^66 + x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 94*x^5 + 116*x^4 + 44*x^3 + 84*x^2 + 105*x + 76, x^73 + 60*x^71 + 120*x^70 + 86*x^69 + 104*x^68 + 124*x^67 + 72*x^66 + 121*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 86*x^5 + 104*x^4 + 60*x^3 + 72*x^2 + 97*x + 88, x^73 + 60*x^71 + 72*x^70 + 22*x^69 + 24*x^68 + 124*x^67 + 120*x^66 + 57*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 22*x^5 + 24*x^4 + 60*x^3 + 120*x^2 + 33*x + 40, x^73 + 60*x^71 + 80*x^70 + 6*x^69 + 64*x^68 + 28*x^67 + 16*x^66 + 41*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 6*x^5 + 64*x^4 + 92*x^3 + 16*x^2 + 17*x + 96, x^73 + 60*x^71 + 60*x^70 + 46*x^69 + 84*x^68 + 76*x^67 + 100*x^66 + 81*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 46*x^5 + 20*x^4 + 12*x^3 + 36*x^2 + 57*x + 76, x^73 + 60*x^71 + 56*x^70 + 70*x^69 + 88*x^68 + 28*x^67 + 104*x^66 + 105*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 70*x^5 + 88*x^4 + 92*x^3 + 104*x^2 + 81*x + 8, x^73 + 60*x^71 + 116*x^70 + 94*x^69 + 108*x^68 + 108*x^67 + 76*x^66 + x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 94*x^5 + 44*x^4 + 44*x^3 + 12*x^2 + 105*x + 20, x^73 + 60*x^71 + 44*x^70 + 62*x^69 + 52*x^68 + 44*x^67 + 20*x^66 + 97*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 62*x^5 + 116*x^4 + 108*x^3 + 84*x^2 + 73*x + 76, x^73 + 60*x^71 + 96*x^70 + 22*x^69 + 64*x^68 + 60*x^67 + 96*x^66 + 121*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 22*x^5 + 64*x^4 + 124*x^3 + 96*x^2 + 97*x, x^73 + 60*x^71 + 88*x^70 + 54*x^69 + 40*x^68 + 124*x^67 + 104*x^66 + 25*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 54*x^5 + 40*x^4 + 60*x^3 + 104*x^2 + x + 24, x^73 + 60*x^71 + 64*x^70 + 6*x^69 + 112*x^68 + 28*x^67 + 96*x^66 + 41*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 6*x^5 + 112*x^4 + 92*x^3 + 96*x^2 + 17*x + 112, x^73 + 60*x^71 + 104*x^70 + 102*x^69 + 8*x^68 + 92*x^67 + 120*x^66 + 9*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 102*x^5 + 8*x^4 + 28*x^3 + 120*x^2 + 113*x + 24, x^73 + 60*x^71 + 88*x^70 + 102*x^69 + 88*x^68 + 92*x^67 + 8*x^66 + 9*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 102*x^5 + 88*x^4 + 28*x^3 + 8*x^2 + 113*x + 72, x^73 + 60*x^71 + 72*x^70 + 118*x^69 + 24*x^68 + 60*x^67 + 120*x^66 + 25*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 118*x^5 + 24*x^4 + 124*x^3 + 120*x^2 + x + 40, x^73 + 60*x^71 + 24*x^70 + 86*x^69 + 104*x^68 + 124*x^67 + 104*x^66 + 121*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 86*x^5 + 104*x^4 + 60*x^3 + 104*x^2 + 97*x + 24, x^73 + 60*x^71 + 36*x^70 + 78*x^69 + 12*x^68 + 12*x^67 + 60*x^66 + 113*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 78*x^5 + 76*x^4 + 76*x^3 + 124*x^2 + 89*x + 84, x^73 + 60*x^71 + 88*x^70 + 38*x^69 + 120*x^68 + 28*x^67 + 8*x^66 + 9*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 38*x^5 + 120*x^4 + 92*x^3 + 8*x^2 + 113*x + 40, x^73 + 60*x^71 + 76*x^70 + 14*x^69 + 68*x^68 + 76*x^67 + 20*x^66 + 113*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 14*x^5 + 4*x^4 + 12*x^3 + 84*x^2 + 89*x + 28, x^73 + 60*x^71 + 28*x^70 + 94*x^69 + 68*x^68 + 44*x^67 + 100*x^66 + 65*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 94*x^5 + 4*x^4 + 108*x^3 + 36*x^2 + 41*x + 124, x^73 + 60*x^71 + 72*x^70 + 54*x^69 + 120*x^68 + 124*x^67 + 120*x^66 + 25*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 54*x^5 + 120*x^4 + 60*x^3 + 120*x^2 + x + 72, x^73 + 60*x^71 + 124*x^70 + 94*x^69 + 4*x^68 + 108*x^67 + 4*x^66 + x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 94*x^5 + 68*x^4 + 44*x^3 + 68*x^2 + 105*x + 60, x^73 + 60*x^71 + 96*x^70 + 86*x^69 + 32*x^68 + 60*x^67 + 32*x^66 + 57*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 86*x^5 + 32*x^4 + 124*x^3 + 32*x^2 + 33*x + 96, x^73 + 60*x^71 + 64*x^70 + 22*x^69 + 96*x^68 + 60*x^67 + 121*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 22*x^5 + 96*x^4 + 124*x^3 + 97*x + 96, x^73 + 60*x^71 + 20*x^70 + 14*x^69 + 92*x^68 + 76*x^67 + 12*x^66 + 113*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 14*x^5 + 28*x^4 + 12*x^3 + 76*x^2 + 89*x + 68, x^73 + 60*x^71 + 96*x^70 + 6*x^69 + 80*x^68 + 28*x^67 + 64*x^66 + 41*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 6*x^5 + 80*x^4 + 92*x^3 + 64*x^2 + 17*x + 16, x^73 + 60*x^71 + 124*x^70 + 62*x^69 + 100*x^68 + 44*x^67 + 68*x^66 + 97*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 62*x^5 + 36*x^4 + 108*x^3 + 4*x^2 + 73*x + 28, x^73 + 60*x^71 + 68*x^70 + 126*x^69 + 28*x^68 + 108*x^67 + 60*x^66 + 97*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 126*x^5 + 92*x^4 + 44*x^3 + 124*x^2 + 73*x + 36, x^73 + 60*x^71 + 120*x^70 + 70*x^69 + 88*x^68 + 92*x^67 + 104*x^66 + 41*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 70*x^5 + 88*x^4 + 28*x^3 + 104*x^2 + 17*x + 72, x^73 + 60*x^71 + 40*x^70 + 118*x^69 + 88*x^68 + 124*x^67 + 24*x^66 + 89*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 118*x^5 + 88*x^4 + 60*x^3 + 24*x^2 + 65*x + 104, x^73 + 60*x^71 + 24*x^70 + 38*x^69 + 24*x^68 + 92*x^67 + 72*x^66 + 73*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 38*x^5 + 24*x^4 + 28*x^3 + 72*x^2 + 49*x + 8, x^73 + 60*x^71 + 20*x^70 + 126*x^69 + 76*x^68 + 44*x^67 + 44*x^66 + 33*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 126*x^5 + 12*x^4 + 108*x^3 + 108*x^2 + 9*x + 52, x^73 + 60*x^71 + 104*x^70 + 86*x^69 + 24*x^68 + 60*x^67 + 88*x^66 + 57*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 86*x^5 + 24*x^4 + 124*x^3 + 88*x^2 + 33*x + 40, x^73 + 60*x^71 + 108*x^70 + 94*x^69 + 116*x^68 + 108*x^67 + 84*x^66 + x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 94*x^5 + 52*x^4 + 44*x^3 + 20*x^2 + 105*x + 12, x^73 + 60*x^71 + 36*x^70 + 62*x^69 + 60*x^68 + 44*x^67 + 28*x^66 + 97*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 62*x^5 + 124*x^4 + 108*x^3 + 92*x^2 + 73*x + 68, x^73 + 60*x^71 + 44*x^70 + 46*x^69 + 36*x^68 + 12*x^67 + 52*x^66 + 17*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 46*x^5 + 100*x^4 + 76*x^3 + 116*x^2 + 121*x + 60, x^73 + 60*x^71 + 40*x^70 + 86*x^69 + 120*x^68 + 124*x^67 + 24*x^66 + 121*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 86*x^5 + 120*x^4 + 60*x^3 + 24*x^2 + 97*x + 72, x^73 + 60*x^71 + 44*x^70 + 46*x^69 + 4*x^68 + 76*x^67 + 52*x^66 + 81*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 46*x^5 + 68*x^4 + 12*x^3 + 116*x^2 + 57*x + 92, x^73 + 60*x^71 + 28*x^70 + 46*x^69 + 116*x^68 + 12*x^67 + 68*x^66 + 17*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 46*x^5 + 52*x^4 + 76*x^3 + 4*x^2 + 121*x + 108, x^73 + 60*x^71 + 16*x^70 + 38*x^69 + 32*x^68 + 92*x^67 + 16*x^66 + 73*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 38*x^5 + 32*x^4 + 28*x^3 + 16*x^2 + 49*x + 64, x^73 + 60*x^71 + 76*x^70 + 78*x^69 + 68*x^68 + 76*x^67 + 20*x^66 + 49*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 78*x^5 + 4*x^4 + 12*x^3 + 84*x^2 + 25*x + 28, x^73 + 60*x^71 + 116*x^70 + 78*x^69 + 124*x^68 + 76*x^67 + 44*x^66 + 49*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 78*x^5 + 60*x^4 + 12*x^3 + 108*x^2 + 25*x + 36, x^73 + 60*x^71 + 120*x^70 + 118*x^69 + 104*x^68 + 60*x^67 + 72*x^66 + 25*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 118*x^5 + 104*x^4 + 124*x^3 + 72*x^2 + x + 88, x^73 + 60*x^71 + 76*x^70 + 126*x^69 + 20*x^68 + 108*x^67 + 52*x^66 + 97*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 126*x^5 + 84*x^4 + 44*x^3 + 116*x^2 + 73*x + 44, x^73 + 60*x^71 + 40*x^70 + 38*x^69 + 104*x^68 + 92*x^67 + 120*x^66 + 73*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 38*x^5 + 104*x^4 + 28*x^3 + 120*x^2 + 49*x + 120, x^73 + 60*x^71 + 104*x^70 + 54*x^69 + 88*x^68 + 124*x^67 + 88*x^66 + 25*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 54*x^5 + 88*x^4 + 60*x^3 + 88*x^2 + x + 104, x^73 + 60*x^71 + 68*x^70 + 14*x^69 + 12*x^68 + 12*x^67 + 92*x^66 + 49*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 14*x^5 + 76*x^4 + 76*x^3 + 28*x^2 + 25*x + 20, x^73 + 60*x^71 + 12*x^70 + 110*x^69 + 68*x^68 + 12*x^67 + 84*x^66 + 81*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 110*x^5 + 4*x^4 + 76*x^3 + 20*x^2 + 57*x + 28, x^73 + 60*x^71 + 32*x^70 + 22*x^69 + 32*x^68 + 124*x^67 + 32*x^66 + 57*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 22*x^5 + 32*x^4 + 60*x^3 + 32*x^2 + 33*x + 32, x^73 + 60*x^71 + 8*x^70 + 22*x^69 + 88*x^68 + 60*x^67 + 120*x^66 + 121*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 22*x^5 + 88*x^4 + 124*x^3 + 120*x^2 + 97*x + 40, x^73 + 60*x^71 + 112*x^70 + 38*x^69 + 32*x^68 + 92*x^67 + 112*x^66 + 73*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 38*x^5 + 32*x^4 + 28*x^3 + 112*x^2 + 49*x, x^73 + 60*x^71 + 108*x^70 + 78*x^69 + 68*x^68 + 12*x^67 + 116*x^66 + 113*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 78*x^5 + 4*x^4 + 76*x^3 + 52*x^2 + 89*x + 28, x^73 + 60*x^71 + 4*x^70 + 126*x^69 + 28*x^68 + 44*x^67 + 60*x^66 + 33*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 126*x^5 + 92*x^4 + 108*x^3 + 124*x^2 + 9*x + 100, x^73 + 60*x^71 + 80*x^70 + 118*x^69 + 16*x^68 + 124*x^67 + 112*x^66 + 89*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 118*x^5 + 16*x^4 + 60*x^3 + 112*x^2 + 65*x + 48, x^73 + 60*x^71 + 84*x^70 + 78*x^69 + 92*x^68 + 12*x^67 + 12*x^66 + 113*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 78*x^5 + 28*x^4 + 76*x^3 + 76*x^2 + 89*x + 4, x^73 + 60*x^71 + 20*x^70 + 46*x^69 + 60*x^68 + 76*x^67 + 12*x^66 + 81*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 46*x^5 + 124*x^4 + 12*x^3 + 76*x^2 + 57*x + 100, x^73 + 60*x^71 + 120*x^70 + 6*x^69 + 88*x^68 + 92*x^67 + 104*x^66 + 105*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 6*x^5 + 88*x^4 + 28*x^3 + 104*x^2 + 81*x + 72, x^73 + 60*x^71 + 80*x^70 + 6*x^69 + 96*x^68 + 92*x^67 + 16*x^66 + 105*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 6*x^5 + 96*x^4 + 28*x^3 + 16*x^2 + 81*x + 64, x^73 + 60*x^71 + 28*x^70 + 30*x^69 + 100*x^68 + 44*x^67 + 36*x^66 + x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 30*x^5 + 36*x^4 + 108*x^3 + 100*x^2 + 105*x + 28, x^73 + 60*x^71 + 8*x^70 + 54*x^69 + 88*x^68 + 124*x^67 + 120*x^66 + 25*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 54*x^5 + 88*x^4 + 60*x^3 + 120*x^2 + x + 40, x^73 + 60*x^71 + 88*x^70 + 70*x^69 + 120*x^68 + 92*x^67 + 8*x^66 + 41*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 70*x^5 + 120*x^4 + 28*x^3 + 8*x^2 + 17*x + 40, x^73 + 60*x^71 + 60*x^70 + 78*x^69 + 20*x^68 + 76*x^67 + 36*x^66 + 49*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 78*x^5 + 84*x^4 + 12*x^3 + 100*x^2 + 25*x + 76, x^73 + 60*x^71 + 32*x^70 + 118*x^69 + 32*x^68 + 60*x^67 + 32*x^66 + 25*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 118*x^5 + 32*x^4 + 124*x^3 + 32*x^2 + x + 32, x^73 + 60*x^71 + 40*x^70 + 38*x^69 + 8*x^68 + 92*x^67 + 56*x^66 + 73*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 38*x^5 + 8*x^4 + 28*x^3 + 56*x^2 + 49*x + 24, x^73 + 60*x^71 + 116*x^70 + 62*x^69 + 76*x^68 + 108*x^67 + 76*x^66 + 33*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 62*x^5 + 12*x^4 + 44*x^3 + 12*x^2 + 9*x + 52, x^73 + 60*x^71 + 76*x^70 + 126*x^69 + 52*x^68 + 44*x^67 + 52*x^66 + 33*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 126*x^5 + 116*x^4 + 108*x^3 + 116*x^2 + 9*x + 12, x^73 + 60*x^71 + 8*x^70 + 54*x^69 + 120*x^68 + 60*x^67 + 120*x^66 + 89*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 54*x^5 + 120*x^4 + 124*x^3 + 120*x^2 + 65*x + 8, x^73 + 60*x^71 + 104*x^70 + 118*x^69 + 120*x^68 + 60*x^67 + 88*x^66 + 25*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 118*x^5 + 120*x^4 + 124*x^3 + 88*x^2 + x + 72, x^73 + 60*x^71 + 124*x^70 + 14*x^69 + 116*x^68 + 12*x^67 + 100*x^66 + 49*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 14*x^5 + 52*x^4 + 76*x^3 + 36*x^2 + 25*x + 108, x^73 + 60*x^71 + 36*x^70 + 30*x^69 + 28*x^68 + 108*x^67 + 92*x^66 + 65*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 30*x^5 + 92*x^4 + 44*x^3 + 28*x^2 + 41*x + 36, x^73 + 60*x^71 + 104*x^70 + 54*x^69 + 56*x^68 + 60*x^67 + 88*x^66 + 89*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 54*x^5 + 56*x^4 + 124*x^3 + 88*x^2 + 65*x + 8, x^73 + 60*x^71 + 104*x^70 + 102*x^69 + 72*x^68 + 28*x^67 + 56*x^66 + 73*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 102*x^5 + 72*x^4 + 92*x^3 + 56*x^2 + 49*x + 24, x^73 + 60*x^71 + 60*x^70 + 94*x^69 + 4*x^68 + 108*x^67 + 68*x^66 + x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 94*x^5 + 68*x^4 + 44*x^3 + 4*x^2 + 105*x + 60, x^73 + 60*x^71 + 52*x^70 + 14*x^69 + 28*x^68 + 12*x^67 + 108*x^66 + 49*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 14*x^5 + 92*x^4 + 76*x^3 + 44*x^2 + 25*x + 4, x^73 + 60*x^71 + 24*x^70 + 38*x^69 + 56*x^68 + 28*x^67 + 72*x^66 + 9*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 38*x^5 + 56*x^4 + 92*x^3 + 72*x^2 + 113*x + 104, x^73 + 60*x^71 + 108*x^70 + 94*x^69 + 20*x^68 + 44*x^67 + 84*x^66 + 65*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 94*x^5 + 84*x^4 + 108*x^3 + 20*x^2 + 41*x + 108, x^73 + 60*x^71 + 80*x^70 + 6*x^69 + 32*x^68 + 28*x^67 + 80*x^66 + 41*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 6*x^5 + 32*x^4 + 92*x^3 + 80*x^2 + 17*x + 64, x^73 + 60*x^71 + 88*x^70 + 6*x^69 + 24*x^68 + 28*x^67 + 8*x^66 + 41*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 6*x^5 + 24*x^4 + 92*x^3 + 8*x^2 + 17*x + 8, x^73 + 60*x^71 + 16*x^70 + 22*x^69 + 112*x^68 + 60*x^67 + 112*x^66 + 121*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 22*x^5 + 112*x^4 + 124*x^3 + 112*x^2 + 97*x + 16, x^73 + 60*x^71 + 64*x^70 + 22*x^69 + 32*x^68 + 124*x^67 + 64*x^66 + 57*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 22*x^5 + 32*x^4 + 60*x^3 + 64*x^2 + 33*x + 96, x^73 + 60*x^71 + 4*x^70 + 110*x^69 + 108*x^68 + 76*x^67 + 92*x^66 + 17*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 110*x^5 + 44*x^4 + 12*x^3 + 28*x^2 + 121*x + 116, x^73 + 60*x^71 + 120*x^70 + 38*x^69 + 120*x^68 + 28*x^67 + 40*x^66 + 9*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 38*x^5 + 120*x^4 + 92*x^3 + 40*x^2 + 113*x + 104, x^73 + 60*x^71 + 80*x^70 + 86*x^69 + 48*x^68 + 60*x^67 + 48*x^66 + 57*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 86*x^5 + 48*x^4 + 124*x^3 + 48*x^2 + 33*x + 80, x^73 + 60*x^71 + 80*x^70 + 22*x^69 + 16*x^68 + 60*x^67 + 112*x^66 + 121*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 22*x^5 + 16*x^4 + 124*x^3 + 112*x^2 + 97*x + 48, x^73 + 60*x^71 + 12*x^70 + 14*x^69 + 100*x^68 + 76*x^67 + 20*x^66 + 113*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 14*x^5 + 36*x^4 + 12*x^3 + 84*x^2 + 89*x + 60, x^73 + 60*x^71 + 52*x^70 + 94*x^69 + 76*x^68 + 44*x^67 + 12*x^66 + 65*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 94*x^5 + 12*x^4 + 108*x^3 + 76*x^2 + 41*x + 52, x^73 + 60*x^71 + 64*x^70 + 70*x^69 + 16*x^68 + 92*x^67 + 96*x^66 + 41*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 70*x^5 + 16*x^4 + 28*x^3 + 96*x^2 + 17*x + 80, x^73 + 60*x^71 + 104*x^70 + 38*x^69 + 8*x^68 + 28*x^67 + 56*x^66 + 9*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 38*x^5 + 8*x^4 + 92*x^3 + 56*x^2 + 113*x + 88, x^73 + 60*x^71 + 118*x^69 + 64*x^68 + 60*x^67 + 64*x^66 + 25*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 118*x^5 + 64*x^4 + 124*x^3 + 64*x^2 + x, x^73 + 60*x^71 + 8*x^70 + 118*x^69 + 24*x^68 + 124*x^67 + 120*x^66 + 89*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 118*x^5 + 24*x^4 + 60*x^3 + 120*x^2 + 65*x + 104, x^73 + 60*x^71 + 100*x^70 + 126*x^69 + 92*x^68 + 108*x^67 + 92*x^66 + 97*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 126*x^5 + 28*x^4 + 44*x^3 + 28*x^2 + 73*x + 36, x^73 + 60*x^71 + 88*x^70 + 118*x^69 + 8*x^68 + 124*x^67 + 40*x^66 + 89*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 118*x^5 + 8*x^4 + 60*x^3 + 40*x^2 + 65*x + 120, x^73 + 60*x^71 + 64*x^70 + 118*x^69 + 64*x^68 + 60*x^67 + 25*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 118*x^5 + 64*x^4 + 124*x^3 + x, x^73 + 60*x^71 + 100*x^70 + 46*x^69 + 44*x^68 + 76*x^67 + 60*x^66 + 81*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 46*x^5 + 108*x^4 + 12*x^3 + 124*x^2 + 57*x + 116, x^73 + 60*x^71 + 96*x^70 + 54*x^69 + 60*x^67 + 32*x^66 + 89*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 54*x^5 + 124*x^3 + 32*x^2 + 65*x, x^73 + 60*x^71 + 60*x^70 + 78*x^69 + 84*x^68 + 76*x^67 + 36*x^66 + 49*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 78*x^5 + 20*x^4 + 12*x^3 + 100*x^2 + 25*x + 12, x^73 + 60*x^71 + 48*x^70 + 86*x^69 + 112*x^68 + 124*x^67 + 80*x^66 + 121*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 86*x^5 + 112*x^4 + 60*x^3 + 80*x^2 + 97*x + 16, x^73 + 60*x^71 + 80*x^70 + 86*x^69 + 80*x^68 + 124*x^67 + 48*x^66 + 121*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 86*x^5 + 80*x^4 + 60*x^3 + 48*x^2 + 97*x + 48, x^73 + 60*x^71 + 96*x^70 + 54*x^69 + 32*x^68 + 60*x^67 + 96*x^66 + 89*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 54*x^5 + 32*x^4 + 124*x^3 + 96*x^2 + 65*x + 32, x^73 + 60*x^71 + 116*x^70 + 78*x^69 + 60*x^68 + 76*x^67 + 44*x^66 + 49*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 78*x^5 + 124*x^4 + 12*x^3 + 108*x^2 + 25*x + 100, x^73 + 60*x^71 + 116*x^70 + 126*x^69 + 12*x^68 + 44*x^67 + 12*x^66 + 33*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 126*x^5 + 76*x^4 + 108*x^3 + 76*x^2 + 9*x + 52, x^73 + 60*x^71 + 72*x^70 + 118*x^69 + 88*x^68 + 124*x^67 + 56*x^66 + 89*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 118*x^5 + 88*x^4 + 60*x^3 + 56*x^2 + 65*x + 40, x^73 + 60*x^71 + 52*x^70 + 30*x^69 + 76*x^68 + 44*x^67 + 12*x^66 + x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 30*x^5 + 12*x^4 + 108*x^3 + 76*x^2 + 105*x + 52, x^73 + 60*x^71 + 60*x^70 + 126*x^69 + 100*x^68 + 108*x^67 + 68*x^66 + 97*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 126*x^5 + 36*x^4 + 44*x^3 + 4*x^2 + 73*x + 92, x^73 + 60*x^71 + 40*x^70 + 86*x^69 + 88*x^68 + 124*x^67 + 88*x^66 + 121*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 86*x^5 + 88*x^4 + 60*x^3 + 88*x^2 + 97*x + 40, x^73 + 60*x^71 + 40*x^70 + 38*x^69 + 40*x^68 + 28*x^67 + 56*x^66 + 9*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 38*x^5 + 40*x^4 + 92*x^3 + 56*x^2 + 113*x + 120, x^73 + 60*x^71 + 96*x^70 + 6*x^69 + 48*x^68 + 28*x^67 + 41*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 6*x^5 + 48*x^4 + 92*x^3 + 17*x + 112, x^73 + 60*x^71 + 48*x^70 + 6*x^69 + 32*x^68 + 92*x^67 + 112*x^66 + 105*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 6*x^5 + 32*x^4 + 28*x^3 + 112*x^2 + 81*x + 64, x^73 + 60*x^71 + 12*x^70 + 46*x^69 + 68*x^68 + 12*x^67 + 84*x^66 + 17*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 46*x^5 + 4*x^4 + 76*x^3 + 20*x^2 + 121*x + 28, x^73 + 60*x^71 + 96*x^70 + 70*x^69 + 112*x^68 + 92*x^67 + 64*x^66 + 41*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 70*x^5 + 112*x^4 + 28*x^3 + 64*x^2 + 17*x + 112, x^73 + 60*x^71 + 108*x^70 + 30*x^69 + 20*x^68 + 44*x^67 + 84*x^66 + x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 30*x^5 + 84*x^4 + 108*x^3 + 20*x^2 + 105*x + 108, x^73 + 60*x^71 + 36*x^70 + 78*x^69 + 76*x^68 + 76*x^67 + 124*x^66 + 49*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 78*x^5 + 12*x^4 + 12*x^3 + 60*x^2 + 25*x + 84, x^73 + 60*x^71 + 100*x^70 + 30*x^69 + 28*x^68 + 44*x^67 + 92*x^66 + x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 30*x^5 + 92*x^4 + 108*x^3 + 28*x^2 + 105*x + 100, x^73 + 60*x^71 + 12*x^70 + 30*x^69 + 20*x^68 + 108*x^67 + 52*x^66 + 65*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 30*x^5 + 84*x^4 + 44*x^3 + 116*x^2 + 41*x + 108, x^73 + 60*x^71 + 48*x^70 + 70*x^69 + 32*x^68 + 92*x^67 + 112*x^66 + 41*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 70*x^5 + 32*x^4 + 28*x^3 + 112*x^2 + 17*x + 64, x^73 + 60*x^71 + 116*x^70 + 110*x^69 + 124*x^68 + 12*x^67 + 44*x^66 + 81*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 110*x^5 + 60*x^4 + 76*x^3 + 108*x^2 + 57*x + 36, x^73 + 60*x^71 + 76*x^70 + 46*x^69 + 4*x^68 + 76*x^67 + 84*x^66 + 81*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 46*x^5 + 68*x^4 + 12*x^3 + 20*x^2 + 57*x + 28, x^73 + 60*x^71 + 92*x^70 + 126*x^69 + 4*x^68 + 108*x^67 + 36*x^66 + 97*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 126*x^5 + 68*x^4 + 44*x^3 + 100*x^2 + 73*x + 60, x^73 + 60*x^71 + 104*x^70 + 54*x^69 + 120*x^68 + 124*x^67 + 24*x^66 + 25*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 54*x^5 + 120*x^4 + 60*x^3 + 24*x^2 + x + 8, x^73 + 60*x^71 + 40*x^70 + 22*x^69 + 120*x^68 + 60*x^67 + 88*x^66 + 121*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 22*x^5 + 120*x^4 + 124*x^3 + 88*x^2 + 97*x + 8, x^73 + 60*x^71 + 6*x^69 + 16*x^68 + 92*x^67 + 32*x^66 + 105*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 6*x^5 + 16*x^4 + 28*x^3 + 32*x^2 + 81*x + 80, x^73 + 60*x^71 + 72*x^70 + 102*x^69 + 40*x^68 + 92*x^67 + 24*x^66 + 9*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 102*x^5 + 40*x^4 + 28*x^3 + 24*x^2 + 113*x + 120, x^73 + 60*x^71 + 40*x^70 + 86*x^69 + 88*x^68 + 60*x^67 + 24*x^66 + 57*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 86*x^5 + 88*x^4 + 124*x^3 + 24*x^2 + 33*x + 104, x^73 + 60*x^71 + 48*x^70 + 86*x^69 + 16*x^68 + 124*x^67 + 16*x^66 + 121*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 86*x^5 + 16*x^4 + 60*x^3 + 16*x^2 + 97*x + 48, x^73 + 60*x^71 + 124*x^70 + 62*x^69 + 36*x^68 + 44*x^67 + 68*x^66 + 97*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 62*x^5 + 100*x^4 + 108*x^3 + 4*x^2 + 73*x + 92, x^73 + 60*x^71 + 20*x^70 + 46*x^69 + 92*x^68 + 12*x^67 + 12*x^66 + 17*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 46*x^5 + 28*x^4 + 76*x^3 + 76*x^2 + 121*x + 68, x^73 + 60*x^71 + 40*x^70 + 22*x^69 + 24*x^68 + 60*x^67 + 24*x^66 + 121*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 22*x^5 + 24*x^4 + 124*x^3 + 24*x^2 + 97*x + 40, x^73 + 60*x^71 + 76*x^70 + 46*x^69 + 36*x^68 + 12*x^67 + 84*x^66 + 17*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 46*x^5 + 100*x^4 + 76*x^3 + 20*x^2 + 121*x + 124, x^73 + 60*x^71 + 76*x^70 + 46*x^69 + 36*x^68 + 76*x^67 + 20*x^66 + 81*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 46*x^5 + 100*x^4 + 12*x^3 + 84*x^2 + 57*x + 60, x^73 + 60*x^71 + 120*x^70 + 102*x^69 + 120*x^68 + 28*x^67 + 40*x^66 + 73*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 102*x^5 + 120*x^4 + 92*x^3 + 40*x^2 + 49*x + 104, x^73 + 60*x^71 + 72*x^70 + 118*x^69 + 56*x^68 + 60*x^67 + 56*x^66 + 25*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 118*x^5 + 56*x^4 + 124*x^3 + 56*x^2 + x + 72, x^73 + 60*x^71 + 60*x^70 + 94*x^69 + 36*x^68 + 108*x^67 + 4*x^66 + x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 94*x^5 + 100*x^4 + 44*x^3 + 68*x^2 + 105*x + 92, x^73 + 60*x^71 + 64*x^70 + 70*x^69 + 80*x^68 + 92*x^67 + 96*x^66 + 41*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 70*x^5 + 80*x^4 + 28*x^3 + 96*x^2 + 17*x + 16, x^73 + 60*x^71 + 24*x^70 + 102*x^69 + 88*x^68 + 28*x^67 + 8*x^66 + 73*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 102*x^5 + 88*x^4 + 92*x^3 + 8*x^2 + 49*x + 8, x^73 + 60*x^71 + 92*x^70 + 78*x^69 + 116*x^68 + 76*x^67 + 4*x^66 + 49*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 78*x^5 + 52*x^4 + 12*x^3 + 68*x^2 + 25*x + 108, x^73 + 60*x^71 + 88*x^70 + 118*x^69 + 72*x^68 + 60*x^67 + 104*x^66 + 25*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 118*x^5 + 72*x^4 + 124*x^3 + 104*x^2 + x + 120, x^73 + 60*x^71 + 20*x^70 + 46*x^69 + 28*x^68 + 76*x^67 + 76*x^66 + 81*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 46*x^5 + 92*x^4 + 12*x^3 + 12*x^2 + 57*x + 68, x^73 + 60*x^71 + 36*x^70 + 62*x^69 + 92*x^68 + 44*x^67 + 92*x^66 + 97*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 62*x^5 + 28*x^4 + 108*x^3 + 28*x^2 + 73*x + 100, x^73 + 60*x^71 + 40*x^70 + 22*x^69 + 56*x^68 + 124*x^67 + 24*x^66 + 57*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 22*x^5 + 56*x^4 + 60*x^3 + 24*x^2 + 33*x + 8, x^73 + 60*x^71 + 72*x^70 + 86*x^69 + 88*x^68 + 60*x^67 + 56*x^66 + 57*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 86*x^5 + 88*x^4 + 124*x^3 + 56*x^2 + 33*x + 40, x^73 + 60*x^71 + 124*x^70 + 78*x^69 + 84*x^68 + 76*x^67 + 100*x^66 + 49*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 78*x^5 + 20*x^4 + 12*x^3 + 36*x^2 + 25*x + 12, x^73 + 60*x^71 + 48*x^70 + 6*x^69 + 64*x^68 + 28*x^67 + 112*x^66 + 41*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 6*x^5 + 64*x^4 + 92*x^3 + 112*x^2 + 17*x + 32, x^73 + 60*x^71 + 44*x^70 + 110*x^69 + 4*x^68 + 76*x^67 + 52*x^66 + 17*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 110*x^5 + 68*x^4 + 12*x^3 + 116*x^2 + 121*x + 92, x^73 + 60*x^71 + 84*x^70 + 78*x^69 + 124*x^68 + 76*x^67 + 12*x^66 + 49*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 78*x^5 + 60*x^4 + 12*x^3 + 76*x^2 + 25*x + 100, x^73 + 60*x^71 + 12*x^70 + 30*x^69 + 116*x^68 + 44*x^67 + 52*x^66 + x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 30*x^5 + 52*x^4 + 108*x^3 + 116*x^2 + 105*x + 12, x^73 + 60*x^71 + 80*x^70 + 22*x^69 + 112*x^68 + 60*x^67 + 48*x^66 + 121*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 22*x^5 + 112*x^4 + 124*x^3 + 48*x^2 + 97*x + 16, x^73 + 60*x^71 + 72*x^70 + 102*x^69 + 40*x^68 + 28*x^67 + 88*x^66 + 73*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 102*x^5 + 40*x^4 + 92*x^3 + 88*x^2 + 49*x + 56, x^73 + 60*x^71 + 52*x^70 + 94*x^69 + 108*x^68 + 108*x^67 + 12*x^66 + x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 94*x^5 + 44*x^4 + 44*x^3 + 76*x^2 + 105*x + 20, x^73 + 60*x^71 + 72*x^70 + 118*x^69 + 120*x^68 + 60*x^67 + 56*x^66 + 25*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 118*x^5 + 120*x^4 + 124*x^3 + 56*x^2 + x + 8, x^73 + 60*x^71 + 24*x^70 + 86*x^69 + 8*x^68 + 60*x^67 + 104*x^66 + 57*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 86*x^5 + 8*x^4 + 124*x^3 + 104*x^2 + 33*x + 120, x^73 + 60*x^71 + 12*x^70 + 30*x^69 + 52*x^68 + 44*x^67 + 52*x^66 + x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 30*x^5 + 116*x^4 + 108*x^3 + 116*x^2 + 105*x + 76, x^73 + 60*x^71 + 32*x^70 + 6*x^69 + 112*x^68 + 92*x^67 + 105*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 6*x^5 + 112*x^4 + 28*x^3 + 81*x + 112, x^73 + 60*x^71 + 8*x^70 + 118*x^69 + 24*x^68 + 60*x^67 + 56*x^66 + 25*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 118*x^5 + 24*x^4 + 124*x^3 + 56*x^2 + x + 40, x^73 + 60*x^71 + 92*x^70 + 94*x^69 + 36*x^68 + 108*x^67 + 36*x^66 + x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 94*x^5 + 100*x^4 + 44*x^3 + 100*x^2 + 105*x + 28, x^73 + 60*x^71 + 36*x^70 + 78*x^69 + 108*x^68 + 76*x^67 + 60*x^66 + 49*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 78*x^5 + 44*x^4 + 12*x^3 + 124*x^2 + 25*x + 116, x^73 + 60*x^71 + 104*x^70 + 22*x^69 + 120*x^68 + 124*x^67 + 88*x^66 + 57*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 22*x^5 + 120*x^4 + 60*x^3 + 88*x^2 + 33*x + 72, x^73 + 60*x^71 + 100*x^70 + 62*x^69 + 124*x^68 + 108*x^67 + 28*x^66 + 33*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 62*x^5 + 60*x^4 + 44*x^3 + 92*x^2 + 9*x + 68, x^73 + 60*x^71 + 96*x^70 + 6*x^69 + 48*x^68 + 92*x^67 + 64*x^66 + 105*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 6*x^5 + 48*x^4 + 28*x^3 + 64*x^2 + 81*x + 48, x^73 + 60*x^71 + 72*x^70 + 102*x^69 + 8*x^68 + 92*x^67 + 88*x^66 + 9*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 102*x^5 + 8*x^4 + 28*x^3 + 88*x^2 + 113*x + 88, x^73 + 60*x^71 + 86*x^69 + 96*x^68 + 60*x^67 + 64*x^66 + 57*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 86*x^5 + 96*x^4 + 124*x^3 + 64*x^2 + 33*x + 96, x^73 + 60*x^71 + 72*x^70 + 6*x^69 + 72*x^68 + 28*x^67 + 88*x^66 + 41*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 6*x^5 + 72*x^4 + 92*x^3 + 88*x^2 + 17*x + 24, x^73 + 60*x^71 + 44*x^70 + 94*x^69 + 20*x^68 + 44*x^67 + 20*x^66 + 65*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 94*x^5 + 84*x^4 + 108*x^3 + 84*x^2 + 41*x + 108, x^73 + 60*x^71 + 92*x^70 + 94*x^69 + 4*x^68 + 44*x^67 + 36*x^66 + 65*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 94*x^5 + 68*x^4 + 108*x^3 + 100*x^2 + 41*x + 60, x^73 + 60*x^71 + 6*x^69 + 80*x^68 + 92*x^67 + 32*x^66 + 105*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 6*x^5 + 80*x^4 + 28*x^3 + 32*x^2 + 81*x + 16, x^73 + 60*x^71 + 4*x^70 + 46*x^69 + 76*x^68 + 12*x^67 + 92*x^66 + 17*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 46*x^5 + 12*x^4 + 76*x^3 + 28*x^2 + 121*x + 20, x^73 + 60*x^71 + 48*x^70 + 38*x^69 + 92*x^67 + 112*x^66 + 73*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 38*x^5 + 28*x^3 + 112*x^2 + 49*x + 96, x^73 + 60*x^71 + 76*x^70 + 110*x^69 + 100*x^68 + 76*x^67 + 20*x^66 + 17*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 110*x^5 + 36*x^4 + 12*x^3 + 84*x^2 + 121*x + 124, x^73 + 60*x^71 + 100*x^70 + 94*x^69 + 28*x^68 + 108*x^67 + 28*x^66 + x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 94*x^5 + 92*x^4 + 44*x^3 + 92*x^2 + 105*x + 36, x^73 + 60*x^71 + 60*x^70 + 110*x^69 + 116*x^68 + 12*x^67 + 100*x^66 + 81*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 110*x^5 + 52*x^4 + 76*x^3 + 36*x^2 + 57*x + 44, x^73 + 60*x^71 + 124*x^70 + 62*x^69 + 4*x^68 + 44*x^67 + 4*x^66 + 97*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 62*x^5 + 68*x^4 + 108*x^3 + 68*x^2 + 73*x + 60, x^73 + 60*x^71 + 32*x^70 + 70*x^69 + 16*x^68 + 28*x^67 + 105*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 70*x^5 + 16*x^4 + 92*x^3 + 81*x + 80, x^73 + 60*x^71 + 76*x^70 + 110*x^69 + 36*x^68 + 12*x^67 + 84*x^66 + 81*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 110*x^5 + 100*x^4 + 76*x^3 + 20*x^2 + 57*x + 124, x^73 + 60*x^71 + 4*x^70 + 62*x^69 + 60*x^68 + 108*x^67 + 60*x^66 + 33*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 62*x^5 + 124*x^4 + 44*x^3 + 124*x^2 + 9*x + 68, x^73 + 60*x^71 + 52*x^70 + 14*x^69 + 60*x^68 + 12*x^67 + 44*x^66 + 49*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 14*x^5 + 124*x^4 + 76*x^3 + 108*x^2 + 25*x + 36, x^73 + 60*x^71 + 28*x^70 + 30*x^69 + 100*x^68 + 108*x^67 + 100*x^66 + 65*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 30*x^5 + 36*x^4 + 44*x^3 + 36*x^2 + 41*x + 92, x^73 + 60*x^71 + 84*x^70 + 30*x^69 + 12*x^68 + 44*x^67 + 44*x^66 + x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 30*x^5 + 76*x^4 + 108*x^3 + 108*x^2 + 105*x + 52, x^73 + 60*x^71 + 16*x^70 + 70*x^69 + 64*x^68 + 92*x^67 + 16*x^66 + 41*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 70*x^5 + 64*x^4 + 28*x^3 + 16*x^2 + 17*x + 32, x^73 + 60*x^71 + 28*x^70 + 30*x^69 + 4*x^68 + 44*x^67 + 100*x^66 + x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 30*x^5 + 68*x^4 + 108*x^3 + 36*x^2 + 105*x + 60, x^73 + 60*x^71 + 124*x^70 + 110*x^69 + 20*x^68 + 12*x^67 + 100*x^66 + 81*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 110*x^5 + 84*x^4 + 76*x^3 + 36*x^2 + 57*x + 76, x^73 + 60*x^71 + 64*x^70 + 118*x^69 + 124*x^67 + 64*x^66 + 89*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 118*x^5 + 60*x^3 + 64*x^2 + 65*x, x^73 + 60*x^71 + 70*x^69 + 112*x^68 + 28*x^67 + 32*x^66 + 105*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 70*x^5 + 112*x^4 + 92*x^3 + 32*x^2 + 81*x + 112, x^73 + 60*x^71 + 4*x^70 + 14*x^69 + 44*x^68 + 76*x^67 + 28*x^66 + 113*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 14*x^5 + 108*x^4 + 12*x^3 + 92*x^2 + 89*x + 116, x^73 + 60*x^71 + 28*x^70 + 78*x^69 + 116*x^68 + 12*x^67 + 4*x^66 + 113*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 78*x^5 + 52*x^4 + 76*x^3 + 68*x^2 + 89*x + 44, x^73 + 60*x^71 + 8*x^70 + 6*x^69 + 72*x^68 + 28*x^67 + 24*x^66 + 41*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 6*x^5 + 72*x^4 + 92*x^3 + 24*x^2 + 17*x + 24, x^73 + 60*x^71 + 32*x^70 + 38*x^69 + 80*x^68 + 28*x^67 + 64*x^66 + 9*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 38*x^5 + 80*x^4 + 92*x^3 + 64*x^2 + 113*x + 80, x^73 + 60*x^71 + 76*x^70 + 46*x^69 + 68*x^68 + 12*x^67 + 20*x^66 + 17*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 46*x^5 + 4*x^4 + 76*x^3 + 84*x^2 + 121*x + 28, x^73 + 60*x^71 + 64*x^70 + 70*x^69 + 48*x^68 + 28*x^67 + 96*x^66 + 105*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 70*x^5 + 48*x^4 + 92*x^3 + 96*x^2 + 81*x + 48, x^73 + 60*x^71 + 56*x^70 + 22*x^69 + 72*x^68 + 124*x^67 + 72*x^66 + 57*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 22*x^5 + 72*x^4 + 60*x^3 + 72*x^2 + 33*x + 56, x^73 + 60*x^71 + 72*x^70 + 70*x^69 + 8*x^68 + 92*x^67 + 24*x^66 + 41*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 70*x^5 + 8*x^4 + 28*x^3 + 24*x^2 + 17*x + 24, x^73 + 60*x^71 + 88*x^70 + 102*x^69 + 56*x^68 + 28*x^67 + 8*x^66 + 73*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 102*x^5 + 56*x^4 + 92*x^3 + 8*x^2 + 49*x + 104, x^73 + 60*x^71 + 24*x^70 + 22*x^69 + 8*x^68 + 60*x^67 + 104*x^66 + 121*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 22*x^5 + 8*x^4 + 124*x^3 + 104*x^2 + 97*x + 120, x^73 + 60*x^71 + 24*x^70 + 54*x^69 + 8*x^68 + 124*x^67 + 104*x^66 + 25*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 54*x^5 + 8*x^4 + 60*x^3 + 104*x^2 + x + 120, x^73 + 60*x^71 + 88*x^70 + 22*x^69 + 8*x^68 + 60*x^67 + 40*x^66 + 121*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 22*x^5 + 8*x^4 + 124*x^3 + 40*x^2 + 97*x + 120, x^73 + 60*x^71 + 76*x^70 + 30*x^69 + 20*x^68 + 108*x^67 + 116*x^66 + 65*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 30*x^5 + 84*x^4 + 44*x^3 + 52*x^2 + 41*x + 108, x^73 + 60*x^71 + 116*x^70 + 62*x^69 + 108*x^68 + 44*x^67 + 76*x^66 + 97*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 62*x^5 + 44*x^4 + 108*x^3 + 12*x^2 + 73*x + 20, x^73 + 60*x^71 + 56*x^70 + 102*x^69 + 24*x^68 + 28*x^67 + 40*x^66 + 73*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 102*x^5 + 24*x^4 + 92*x^3 + 40*x^2 + 49*x + 8, x^73 + 60*x^71 + 6*x^69 + 16*x^68 + 28*x^67 + 96*x^66 + 41*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 6*x^5 + 16*x^4 + 92*x^3 + 96*x^2 + 17*x + 16, x^73 + 60*x^71 + 72*x^70 + 22*x^69 + 88*x^68 + 124*x^67 + 120*x^66 + 57*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 22*x^5 + 88*x^4 + 60*x^3 + 120*x^2 + 33*x + 104, x^73 + 60*x^71 + 68*x^70 + 126*x^69 + 28*x^68 + 44*x^67 + 124*x^66 + 33*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 126*x^5 + 92*x^4 + 108*x^3 + 60*x^2 + 9*x + 100, x^73 + 60*x^71 + 72*x^70 + 6*x^69 + 104*x^68 + 92*x^67 + 88*x^66 + 105*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 6*x^5 + 104*x^4 + 28*x^3 + 88*x^2 + 81*x + 120, x^73 + 60*x^71 + 80*x^70 + 22*x^69 + 48*x^68 + 60*x^67 + 48*x^66 + 121*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 22*x^5 + 48*x^4 + 124*x^3 + 48*x^2 + 97*x + 80, x^73 + 60*x^71 + 32*x^70 + 70*x^69 + 80*x^68 + 28*x^67 + 105*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 70*x^5 + 80*x^4 + 92*x^3 + 81*x + 16, x^73 + 60*x^71 + 124*x^70 + 126*x^69 + 68*x^68 + 108*x^67 + 68*x^66 + 97*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 126*x^5 + 4*x^4 + 44*x^3 + 4*x^2 + 73*x + 60, x^73 + 60*x^71 + 48*x^70 + 118*x^69 + 80*x^68 + 124*x^67 + 80*x^66 + 89*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 118*x^5 + 80*x^4 + 60*x^3 + 80*x^2 + 65*x + 48, x^73 + 60*x^71 + 32*x^70 + 22*x^69 + 32*x^68 + 60*x^67 + 96*x^66 + 121*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 22*x^5 + 32*x^4 + 124*x^3 + 96*x^2 + 97*x + 96, x^73 + 60*x^71 + 20*x^70 + 110*x^69 + 92*x^68 + 76*x^67 + 76*x^66 + 17*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 110*x^5 + 28*x^4 + 12*x^3 + 12*x^2 + 121*x + 4, x^73 + 60*x^71 + 56*x^70 + 6*x^69 + 56*x^68 + 28*x^67 + 40*x^66 + 41*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 6*x^5 + 56*x^4 + 92*x^3 + 40*x^2 + 17*x + 104, x^73 + 60*x^71 + 76*x^70 + 110*x^69 + 68*x^68 + 76*x^67 + 84*x^66 + 17*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 110*x^5 + 4*x^4 + 12*x^3 + 20*x^2 + 121*x + 92, x^73 + 60*x^71 + 68*x^70 + 46*x^69 + 44*x^68 + 76*x^67 + 28*x^66 + 81*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 46*x^5 + 108*x^4 + 12*x^3 + 92*x^2 + 57*x + 52, x^73 + 60*x^71 + 24*x^70 + 6*x^69 + 56*x^68 + 28*x^67 + 8*x^66 + 41*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 6*x^5 + 56*x^4 + 92*x^3 + 8*x^2 + 17*x + 40, x^73 + 60*x^71 + 92*x^70 + 94*x^69 + 36*x^68 + 44*x^67 + 100*x^66 + 65*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 94*x^5 + 100*x^4 + 108*x^3 + 36*x^2 + 41*x + 92, x^73 + 60*x^71 + 92*x^70 + 110*x^69 + 116*x^68 + 12*x^67 + 4*x^66 + 81*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 110*x^5 + 52*x^4 + 76*x^3 + 68*x^2 + 57*x + 108, x^73 + 60*x^71 + 76*x^70 + 30*x^69 + 116*x^68 + 44*x^67 + 116*x^66 + x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 30*x^5 + 52*x^4 + 108*x^3 + 52*x^2 + 105*x + 12, x^73 + 60*x^71 + 116*x^70 + 30*x^69 + 76*x^68 + 108*x^67 + 12*x^66 + 65*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 30*x^5 + 12*x^4 + 44*x^3 + 76*x^2 + 41*x + 116, x^73 + 60*x^71 + 60*x^70 + 46*x^69 + 52*x^68 + 76*x^67 + 36*x^66 + 81*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 46*x^5 + 116*x^4 + 12*x^3 + 100*x^2 + 57*x + 44, x^73 + 60*x^71 + 96*x^70 + 22*x^69 + 64*x^68 + 124*x^67 + 32*x^66 + 57*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 22*x^5 + 64*x^4 + 60*x^3 + 32*x^2 + 33*x + 64, x^73 + 60*x^71 + 108*x^70 + 94*x^69 + 52*x^68 + 44*x^67 + 20*x^66 + 65*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 94*x^5 + 116*x^4 + 108*x^3 + 84*x^2 + 41*x + 12, x^73 + 60*x^71 + 70*x^69 + 48*x^68 + 92*x^67 + 96*x^66 + 41*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 70*x^5 + 48*x^4 + 28*x^3 + 96*x^2 + 17*x + 112, x^73 + 60*x^71 + 88*x^70 + 102*x^69 + 24*x^68 + 92*x^67 + 8*x^66 + 9*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 102*x^5 + 24*x^4 + 28*x^3 + 8*x^2 + 113*x + 8, x^73 + 60*x^71 + 84*x^70 + 110*x^69 + 124*x^68 + 12*x^67 + 12*x^66 + 81*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 110*x^5 + 60*x^4 + 76*x^3 + 76*x^2 + 57*x + 100, x^73 + 60*x^71 + 12*x^70 + 126*x^69 + 20*x^68 + 108*x^67 + 116*x^66 + 97*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 126*x^5 + 84*x^4 + 44*x^3 + 52*x^2 + 73*x + 44, x^73 + 60*x^71 + 108*x^70 + 126*x^69 + 116*x^68 + 108*x^67 + 20*x^66 + 97*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 126*x^5 + 52*x^4 + 44*x^3 + 84*x^2 + 73*x + 76, x^73 + 60*x^71 + 84*x^70 + 126*x^69 + 76*x^68 + 44*x^67 + 108*x^66 + 33*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 126*x^5 + 12*x^4 + 108*x^3 + 44*x^2 + 9*x + 52, x^73 + 60*x^71 + 60*x^70 + 94*x^69 + 100*x^68 + 108*x^67 + 4*x^66 + x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 94*x^5 + 36*x^4 + 44*x^3 + 68*x^2 + 105*x + 28, x^73 + 60*x^71 + 64*x^70 + 86*x^69 + 96*x^68 + 60*x^67 + 57*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 86*x^5 + 96*x^4 + 124*x^3 + 33*x + 96, x^73 + 60*x^71 + 4*x^70 + 46*x^69 + 44*x^68 + 12*x^67 + 28*x^66 + 17*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 46*x^5 + 108*x^4 + 76*x^3 + 92*x^2 + 121*x + 116, x^73 + 60*x^71 + 64*x^70 + 38*x^69 + 48*x^68 + 28*x^67 + 32*x^66 + 9*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 38*x^5 + 48*x^4 + 92*x^3 + 32*x^2 + 113*x + 112, x^73 + 60*x^71 + 56*x^70 + 86*x^69 + 104*x^68 + 124*x^67 + 8*x^66 + 121*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 86*x^5 + 104*x^4 + 60*x^3 + 8*x^2 + 97*x + 88, x^73 + 60*x^71 + 92*x^70 + 30*x^69 + 36*x^68 + 44*x^67 + 100*x^66 + x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 30*x^5 + 100*x^4 + 108*x^3 + 36*x^2 + 105*x + 92, x^73 + 60*x^71 + 8*x^70 + 38*x^69 + 8*x^68 + 92*x^67 + 24*x^66 + 73*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 38*x^5 + 8*x^4 + 28*x^3 + 24*x^2 + 49*x + 88, x^73 + 60*x^71 + 56*x^70 + 54*x^69 + 40*x^68 + 124*x^67 + 72*x^66 + 25*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 54*x^5 + 40*x^4 + 60*x^3 + 72*x^2 + x + 88, x^73 + 60*x^71 + 8*x^70 + 102*x^69 + 72*x^68 + 92*x^67 + 24*x^66 + 9*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 102*x^5 + 72*x^4 + 28*x^3 + 24*x^2 + 113*x + 24, x^73 + 60*x^71 + 108*x^70 + 30*x^69 + 52*x^68 + 44*x^67 + 20*x^66 + x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 30*x^5 + 116*x^4 + 108*x^3 + 84*x^2 + 105*x + 12, x^73 + 60*x^71 + 4*x^70 + 62*x^69 + 28*x^68 + 108*x^67 + 124*x^66 + 33*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 62*x^5 + 92*x^4 + 44*x^3 + 60*x^2 + 9*x + 36, x^73 + 60*x^71 + 72*x^70 + 22*x^69 + 24*x^68 + 60*x^67 + 56*x^66 + 121*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 22*x^5 + 24*x^4 + 124*x^3 + 56*x^2 + 97*x + 104, x^73 + 60*x^71 + 116*x^70 + 14*x^69 + 124*x^68 + 76*x^67 + 44*x^66 + 113*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 14*x^5 + 60*x^4 + 12*x^3 + 108*x^2 + 89*x + 36, x^73 + 60*x^71 + 104*x^70 + 118*x^69 + 88*x^68 + 60*x^67 + 24*x^66 + 25*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 118*x^5 + 88*x^4 + 124*x^3 + 24*x^2 + x + 40, x^73 + 60*x^71 + 80*x^70 + 70*x^69 + 92*x^67 + 80*x^66 + 41*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 70*x^5 + 28*x^3 + 80*x^2 + 17*x + 96, x^73 + 60*x^71 + 108*x^70 + 110*x^69 + 36*x^68 + 12*x^67 + 116*x^66 + 81*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 110*x^5 + 100*x^4 + 76*x^3 + 52*x^2 + 57*x + 60, x^73 + 60*x^71 + 72*x^70 + 70*x^69 + 40*x^68 + 28*x^67 + 24*x^66 + 105*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 70*x^5 + 40*x^4 + 92*x^3 + 24*x^2 + 81*x + 120, x^73 + 60*x^71 + 28*x^70 + 94*x^69 + 4*x^68 + 44*x^67 + 100*x^66 + 65*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 94*x^5 + 68*x^4 + 108*x^3 + 36*x^2 + 41*x + 60, x^73 + 60*x^71 + 76*x^70 + 94*x^69 + 84*x^68 + 108*x^67 + 116*x^66 + x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 56*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 94*x^5 + 20*x^4 + 44*x^3 + 52*x^2 + 105*x + 44, x^73 + 60*x^71 + 64*x^70 + 86*x^69 + 60*x^67 + 64*x^66 + 57*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 86*x^5 + 124*x^3 + 64*x^2 + 33*x, x^73 + 60*x^71 + 32*x^70 + 54*x^69 + 124*x^67 + 32*x^66 + 25*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 40*x^35 + 64*x^34 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 54*x^5 + 60*x^3 + 32*x^2 + x + 64, x^73 + 60*x^71 + 32*x^70 + 54*x^69 + 32*x^68 + 124*x^67 + 96*x^66 + 25*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 54*x^5 + 32*x^4 + 60*x^3 + 96*x^2 + x + 96, x^73 + 60*x^71 + 36*x^70 + 94*x^69 + 60*x^68 + 44*x^67 + 92*x^66 + 65*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 94*x^5 + 124*x^4 + 108*x^3 + 28*x^2 + 41*x + 4, x^73 + 60*x^71 + 20*x^70 + 94*x^69 + 108*x^68 + 44*x^67 + 44*x^66 + 65*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 94*x^5 + 44*x^4 + 108*x^3 + 108*x^2 + 41*x + 20, x^73 + 60*x^71 + 20*x^70 + 78*x^69 + 60*x^68 + 12*x^67 + 12*x^66 + 113*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 78*x^5 + 124*x^4 + 76*x^3 + 76*x^2 + 89*x + 100, x^73 + 60*x^71 + 88*x^70 + 70*x^69 + 24*x^68 + 28*x^67 + 8*x^66 + 105*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 70*x^5 + 24*x^4 + 92*x^3 + 8*x^2 + 81*x + 8, x^73 + 60*x^71 + 52*x^70 + 46*x^69 + 124*x^68 + 76*x^67 + 44*x^66 + 81*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 46*x^5 + 60*x^4 + 12*x^3 + 108*x^2 + 57*x + 100, x^73 + 60*x^71 + 116*x^70 + 126*x^69 + 76*x^68 + 108*x^67 + 76*x^66 + 97*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 126*x^5 + 12*x^4 + 44*x^3 + 12*x^2 + 73*x + 52, x^73 + 60*x^71 + 20*x^70 + 30*x^69 + 12*x^68 + 108*x^67 + 44*x^66 + 65*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 30*x^5 + 76*x^4 + 44*x^3 + 108*x^2 + 41*x + 116, x^73 + 60*x^71 + 44*x^70 + 94*x^69 + 52*x^68 + 44*x^67 + 84*x^66 + 65*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 94*x^5 + 116*x^4 + 108*x^3 + 20*x^2 + 41*x + 12, x^73 + 60*x^71 + 108*x^70 + 46*x^69 + 4*x^68 + 76*x^67 + 116*x^66 + 81*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 46*x^5 + 68*x^4 + 12*x^3 + 52*x^2 + 57*x + 92, x^73 + 60*x^71 + 36*x^70 + 126*x^69 + 60*x^68 + 108*x^67 + 92*x^66 + 97*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 126*x^5 + 124*x^4 + 44*x^3 + 28*x^2 + 73*x + 4, x^73 + 60*x^71 + 104*x^70 + 70*x^69 + 40*x^68 + 92*x^67 + 120*x^66 + 41*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 70*x^5 + 40*x^4 + 28*x^3 + 120*x^2 + 17*x + 120, x^73 + 60*x^71 + 70*x^69 + 112*x^68 + 92*x^67 + 96*x^66 + 41*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 70*x^5 + 112*x^4 + 28*x^3 + 96*x^2 + 17*x + 48, x^73 + 60*x^71 + 56*x^70 + 102*x^69 + 56*x^68 + 92*x^67 + 40*x^66 + 9*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 102*x^5 + 56*x^4 + 28*x^3 + 40*x^2 + 113*x + 104, x^73 + 60*x^71 + 40*x^70 + 86*x^69 + 120*x^68 + 60*x^67 + 88*x^66 + 57*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 86*x^5 + 120*x^4 + 124*x^3 + 88*x^2 + 33*x + 8, x^73 + 60*x^71 + 68*x^70 + 110*x^69 + 108*x^68 + 12*x^67 + 92*x^66 + 81*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 110*x^5 + 44*x^4 + 76*x^3 + 28*x^2 + 57*x + 52, x^73 + 60*x^71 + 44*x^70 + 126*x^69 + 84*x^68 + 44*x^67 + 84*x^66 + 33*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 126*x^5 + 20*x^4 + 108*x^3 + 20*x^2 + 9*x + 108, x^73 + 60*x^71 + 88*x^70 + 54*x^69 + 104*x^68 + 60*x^67 + 40*x^66 + 89*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 54*x^5 + 104*x^4 + 124*x^3 + 40*x^2 + 65*x + 24, x^73 + 60*x^71 + 64*x^70 + 38*x^69 + 112*x^68 + 28*x^67 + 32*x^66 + 9*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 38*x^5 + 112*x^4 + 92*x^3 + 32*x^2 + 113*x + 48, x^73 + 60*x^71 + 120*x^70 + 54*x^69 + 104*x^68 + 60*x^67 + 72*x^66 + 89*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 54*x^5 + 104*x^4 + 124*x^3 + 72*x^2 + 65*x + 88, x^73 + 60*x^71 + 24*x^70 + 54*x^69 + 72*x^68 + 60*x^67 + 40*x^66 + 89*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 54*x^5 + 72*x^4 + 124*x^3 + 40*x^2 + 65*x + 120, x^73 + 60*x^71 + 88*x^70 + 86*x^69 + 72*x^68 + 60*x^67 + 40*x^66 + 57*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 86*x^5 + 72*x^4 + 124*x^3 + 40*x^2 + 33*x + 56, x^73 + 60*x^71 + 52*x^70 + 110*x^69 + 124*x^68 + 12*x^67 + 108*x^66 + 81*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 110*x^5 + 60*x^4 + 76*x^3 + 44*x^2 + 57*x + 36, x^73 + 60*x^71 + 84*x^70 + 78*x^69 + 92*x^68 + 76*x^67 + 76*x^66 + 49*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 78*x^5 + 28*x^4 + 12*x^3 + 12*x^2 + 25*x + 68, x^73 + 60*x^71 + 88*x^70 + 38*x^69 + 56*x^68 + 28*x^67 + 8*x^66 + 9*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 38*x^5 + 56*x^4 + 92*x^3 + 8*x^2 + 113*x + 104, x^73 + 60*x^71 + 12*x^70 + 78*x^69 + 4*x^68 + 76*x^67 + 84*x^66 + 49*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 78*x^5 + 68*x^4 + 12*x^3 + 20*x^2 + 25*x + 92, x^73 + 60*x^71 + 20*x^70 + 110*x^69 + 124*x^68 + 76*x^67 + 12*x^66 + 17*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 110*x^5 + 60*x^4 + 12*x^3 + 76*x^2 + 121*x + 36, x^73 + 60*x^71 + 112*x^70 + 86*x^69 + 48*x^68 + 60*x^67 + 80*x^66 + 57*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 86*x^5 + 48*x^4 + 124*x^3 + 80*x^2 + 33*x + 16, x^73 + 60*x^71 + 72*x^70 + 70*x^69 + 72*x^68 + 92*x^67 + 24*x^66 + 41*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 70*x^5 + 72*x^4 + 28*x^3 + 24*x^2 + 17*x + 88, x^73 + 60*x^71 + 60*x^70 + 62*x^69 + 4*x^68 + 44*x^67 + 68*x^66 + 97*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 62*x^5 + 68*x^4 + 108*x^3 + 4*x^2 + 73*x + 60, x^73 + 60*x^71 + 52*x^70 + 46*x^69 + 60*x^68 + 76*x^67 + 44*x^66 + 81*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 46*x^5 + 124*x^4 + 12*x^3 + 108*x^2 + 57*x + 36, x^73 + 60*x^71 + 28*x^70 + 46*x^69 + 116*x^68 + 76*x^67 + 4*x^66 + 81*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 46*x^5 + 52*x^4 + 12*x^3 + 68*x^2 + 57*x + 44, x^73 + 60*x^71 + 32*x^70 + 22*x^69 + 60*x^67 + 32*x^66 + 121*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 22*x^5 + 124*x^3 + 32*x^2 + 97*x + 64, x^73 + 60*x^71 + 60*x^70 + 30*x^69 + 100*x^68 + 44*x^67 + 68*x^66 + x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 30*x^5 + 36*x^4 + 108*x^3 + 4*x^2 + 105*x + 92, x^73 + 60*x^71 + 44*x^70 + 14*x^69 + 100*x^68 + 12*x^67 + 116*x^66 + 49*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 14*x^5 + 36*x^4 + 76*x^3 + 52*x^2 + 25*x + 60, x^73 + 60*x^71 + 8*x^70 + 54*x^69 + 56*x^68 + 60*x^67 + 120*x^66 + 89*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 54*x^5 + 56*x^4 + 124*x^3 + 120*x^2 + 65*x + 72, x^73 + 60*x^71 + 120*x^70 + 102*x^69 + 56*x^68 + 92*x^67 + 104*x^66 + 9*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 102*x^5 + 56*x^4 + 28*x^3 + 104*x^2 + 113*x + 104, x^73 + 60*x^71 + 40*x^70 + 86*x^69 + 24*x^68 + 60*x^67 + 24*x^66 + 57*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 86*x^5 + 24*x^4 + 124*x^3 + 24*x^2 + 33*x + 40, x^73 + 60*x^71 + 32*x^70 + 86*x^69 + 124*x^67 + 96*x^66 + 121*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 86*x^5 + 60*x^3 + 96*x^2 + 97*x, x^73 + 60*x^71 + 124*x^70 + 110*x^69 + 84*x^68 + 12*x^67 + 100*x^66 + 81*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 110*x^5 + 20*x^4 + 76*x^3 + 36*x^2 + 57*x + 12, x^73 + 60*x^71 + 80*x^70 + 70*x^69 + 64*x^68 + 28*x^67 + 16*x^66 + 105*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 70*x^5 + 64*x^4 + 92*x^3 + 16*x^2 + 81*x + 96, x^73 + 60*x^71 + 44*x^70 + 110*x^69 + 4*x^68 + 12*x^67 + 116*x^66 + 81*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 110*x^5 + 68*x^4 + 76*x^3 + 52*x^2 + 57*x + 28, x^73 + 60*x^71 + 88*x^70 + 118*x^69 + 8*x^68 + 60*x^67 + 104*x^66 + 25*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 118*x^5 + 8*x^4 + 124*x^3 + 104*x^2 + x + 56, x^73 + 60*x^71 + 72*x^70 + 86*x^69 + 120*x^68 + 124*x^67 + 56*x^66 + 121*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 86*x^5 + 120*x^4 + 60*x^3 + 56*x^2 + 97*x + 8, x^73 + 60*x^71 + 52*x^70 + 62*x^69 + 76*x^68 + 44*x^67 + 76*x^66 + 97*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 62*x^5 + 12*x^4 + 108*x^3 + 12*x^2 + 73*x + 116, x^73 + 60*x^71 + 84*x^70 + 46*x^69 + 60*x^68 + 76*x^67 + 76*x^66 + 81*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 46*x^5 + 124*x^4 + 12*x^3 + 12*x^2 + 57*x + 100, x^73 + 60*x^71 + 44*x^70 + 30*x^69 + 52*x^68 + 108*x^67 + 20*x^66 + 65*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 30*x^5 + 116*x^4 + 44*x^3 + 84*x^2 + 41*x + 76, x^73 + 60*x^71 + 96*x^70 + 86*x^69 + 64*x^68 + 60*x^67 + 96*x^66 + 57*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 40*x^35 + 64*x^34 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 86*x^5 + 64*x^4 + 124*x^3 + 96*x^2 + 33*x, x^73 + 60*x^71 + 68*x^70 + 14*x^69 + 12*x^68 + 76*x^67 + 28*x^66 + 113*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 14*x^5 + 76*x^4 + 12*x^3 + 92*x^2 + 89*x + 84, x^73 + 60*x^71 + 104*x^70 + 38*x^69 + 104*x^68 + 92*x^67 + 56*x^66 + 73*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 38*x^5 + 104*x^4 + 28*x^3 + 56*x^2 + 49*x + 120, x^73 + 60*x^71 + 108*x^70 + 14*x^69 + 4*x^68 + 12*x^67 + 116*x^66 + 49*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 14*x^5 + 68*x^4 + 76*x^3 + 52*x^2 + 25*x + 92, x^73 + 60*x^71 + 36*x^70 + 46*x^69 + 12*x^68 + 76*x^67 + 60*x^66 + 81*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 46*x^5 + 76*x^4 + 12*x^3 + 124*x^2 + 57*x + 84, x^73 + 60*x^71 + 32*x^70 + 38*x^69 + 48*x^68 + 92*x^67 + 64*x^66 + 73*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 38*x^5 + 48*x^4 + 28*x^3 + 64*x^2 + 49*x + 112, x^73 + 60*x^71 + 20*x^70 + 46*x^69 + 124*x^68 + 12*x^67 + 76*x^66 + 17*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 46*x^5 + 60*x^4 + 76*x^3 + 12*x^2 + 121*x + 100, x^73 + 60*x^71 + 100*x^70 + 110*x^69 + 76*x^68 + 12*x^67 + 60*x^66 + 81*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 110*x^5 + 12*x^4 + 76*x^3 + 124*x^2 + 57*x + 84, x^73 + 60*x^71 + 20*x^70 + 14*x^69 + 92*x^68 + 12*x^67 + 76*x^66 + 49*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 14*x^5 + 28*x^4 + 76*x^3 + 12*x^2 + 25*x + 4, x^73 + 60*x^71 + 40*x^70 + 54*x^69 + 88*x^68 + 124*x^67 + 24*x^66 + 25*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 54*x^5 + 88*x^4 + 60*x^3 + 24*x^2 + x + 104, x^73 + 60*x^71 + 124*x^70 + 14*x^69 + 116*x^68 + 76*x^67 + 36*x^66 + 113*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 14*x^5 + 52*x^4 + 12*x^3 + 100*x^2 + 89*x + 44, x^73 + 60*x^71 + 12*x^70 + 110*x^69 + 100*x^68 + 76*x^67 + 84*x^66 + 17*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 110*x^5 + 36*x^4 + 12*x^3 + 20*x^2 + 121*x + 124, x^73 + 60*x^71 + 6*x^69 + 80*x^68 + 28*x^67 + 96*x^66 + 41*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 6*x^5 + 80*x^4 + 92*x^3 + 96*x^2 + 17*x + 80, x^73 + 60*x^71 + 68*x^70 + 78*x^69 + 76*x^68 + 12*x^67 + 92*x^66 + 113*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 78*x^5 + 12*x^4 + 76*x^3 + 28*x^2 + 89*x + 84, x^73 + 60*x^71 + 84*x^70 + 46*x^69 + 92*x^68 + 12*x^67 + 76*x^66 + 17*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 46*x^5 + 28*x^4 + 76*x^3 + 12*x^2 + 121*x + 68, x^73 + 60*x^71 + 48*x^70 + 102*x^69 + 32*x^68 + 92*x^67 + 48*x^66 + 9*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 102*x^5 + 32*x^4 + 28*x^3 + 48*x^2 + 113*x, x^73 + 60*x^71 + 96*x^70 + 70*x^69 + 16*x^68 + 92*x^67 + 41*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 70*x^5 + 16*x^4 + 28*x^3 + 17*x + 16, x^73 + 60*x^71 + 68*x^70 + 62*x^69 + 60*x^68 + 108*x^67 + 124*x^66 + 33*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 62*x^5 + 124*x^4 + 44*x^3 + 60*x^2 + 9*x + 68, x^73 + 60*x^71 + 12*x^70 + 78*x^69 + 100*x^68 + 12*x^67 + 84*x^66 + 113*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 78*x^5 + 36*x^4 + 76*x^3 + 20*x^2 + 89*x + 124, x^73 + 60*x^71 + 56*x^70 + 38*x^69 + 56*x^68 + 28*x^67 + 104*x^66 + 9*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 38*x^5 + 56*x^4 + 92*x^3 + 104*x^2 + 113*x + 40, x^73 + 60*x^71 + 54*x^69 + 60*x^67 + 64*x^66 + 89*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 54*x^5 + 124*x^3 + 64*x^2 + 65*x + 64, x^73 + 60*x^71 + 36*x^70 + 78*x^69 + 44*x^68 + 76*x^67 + 60*x^66 + 49*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 78*x^5 + 108*x^4 + 12*x^3 + 124*x^2 + 25*x + 52, x^73 + 60*x^71 + 32*x^70 + 38*x^69 + 16*x^68 + 28*x^67 + 64*x^66 + 9*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 38*x^5 + 16*x^4 + 92*x^3 + 64*x^2 + 113*x + 16, x^73 + 60*x^71 + 84*x^70 + 46*x^69 + 60*x^68 + 12*x^67 + 12*x^66 + 17*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 46*x^5 + 124*x^4 + 76*x^3 + 76*x^2 + 121*x + 36, x^73 + 60*x^71 + 64*x^70 + 54*x^69 + 64*x^68 + 60*x^67 + 89*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 54*x^5 + 64*x^4 + 124*x^3 + 65*x, x^73 + 60*x^71 + 40*x^70 + 22*x^69 + 120*x^68 + 124*x^67 + 24*x^66 + 57*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 22*x^5 + 120*x^4 + 60*x^3 + 24*x^2 + 33*x + 72, x^73 + 60*x^71 + 40*x^70 + 102*x^69 + 8*x^68 + 28*x^67 + 120*x^66 + 73*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 102*x^5 + 8*x^4 + 92*x^3 + 120*x^2 + 49*x + 88, x^73 + 60*x^71 + 100*x^70 + 46*x^69 + 44*x^68 + 12*x^67 + 124*x^66 + 17*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 46*x^5 + 108*x^4 + 76*x^3 + 60*x^2 + 121*x + 52, x^73 + 60*x^71 + 76*x^70 + 14*x^69 + 4*x^68 + 76*x^67 + 20*x^66 + 113*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 14*x^5 + 68*x^4 + 12*x^3 + 84*x^2 + 89*x + 92, x^73 + 60*x^71 + 80*x^70 + 70*x^69 + 64*x^68 + 92*x^67 + 80*x^66 + 41*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 70*x^5 + 64*x^4 + 28*x^3 + 80*x^2 + 17*x + 32, x^73 + 60*x^71 + 124*x^70 + 78*x^69 + 84*x^68 + 12*x^67 + 36*x^66 + 113*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 78*x^5 + 20*x^4 + 76*x^3 + 100*x^2 + 89*x + 76, x^73 + 60*x^71 + 92*x^70 + 110*x^69 + 20*x^68 + 12*x^67 + 68*x^66 + 81*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 110*x^5 + 84*x^4 + 76*x^3 + 4*x^2 + 57*x + 12, x^73 + 60*x^71 + 60*x^70 + 62*x^69 + 100*x^68 + 108*x^67 + 68*x^66 + 33*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 62*x^5 + 36*x^4 + 44*x^3 + 4*x^2 + 9*x + 92, x^73 + 60*x^71 + 60*x^70 + 94*x^69 + 4*x^68 + 44*x^67 + 4*x^66 + 65*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 94*x^5 + 68*x^4 + 108*x^3 + 68*x^2 + 41*x + 124, x^73 + 60*x^71 + 52*x^70 + 62*x^69 + 12*x^68 + 44*x^67 + 76*x^66 + 97*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 62*x^5 + 76*x^4 + 108*x^3 + 12*x^2 + 73*x + 52, x^73 + 60*x^71 + 60*x^70 + 62*x^69 + 36*x^68 + 44*x^67 + 4*x^66 + 97*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 62*x^5 + 100*x^4 + 108*x^3 + 68*x^2 + 73*x + 92, x^73 + 60*x^71 + 96*x^70 + 118*x^69 + 96*x^68 + 124*x^67 + 32*x^66 + 89*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 118*x^5 + 96*x^4 + 60*x^3 + 32*x^2 + 65*x + 32, x^73 + 60*x^71 + 64*x^70 + 54*x^69 + 60*x^67 + 89*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 54*x^5 + 124*x^3 + 65*x + 64, x^73 + 60*x^71 + 8*x^70 + 54*x^69 + 88*x^68 + 60*x^67 + 56*x^66 + 89*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 54*x^5 + 88*x^4 + 124*x^3 + 56*x^2 + 65*x + 104, x^73 + 60*x^71 + 60*x^70 + 14*x^69 + 84*x^68 + 76*x^67 + 36*x^66 + 113*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 14*x^5 + 20*x^4 + 12*x^3 + 100*x^2 + 89*x + 12, x^73 + 60*x^71 + 84*x^70 + 14*x^69 + 124*x^68 + 76*x^67 + 12*x^66 + 113*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 14*x^5 + 60*x^4 + 12*x^3 + 76*x^2 + 89*x + 100, x^73 + 60*x^71 + 76*x^70 + 126*x^69 + 116*x^68 + 44*x^67 + 52*x^66 + 33*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 126*x^5 + 52*x^4 + 108*x^3 + 116*x^2 + 9*x + 76, x^73 + 60*x^71 + 4*x^70 + 30*x^69 + 28*x^68 + 108*x^67 + 60*x^66 + 65*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 30*x^5 + 92*x^4 + 44*x^3 + 124*x^2 + 41*x + 100, x^73 + 60*x^71 + 40*x^70 + 118*x^69 + 120*x^68 + 60*x^67 + 24*x^66 + 25*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 118*x^5 + 120*x^4 + 124*x^3 + 24*x^2 + x + 72, x^73 + 60*x^71 + 32*x^70 + 118*x^69 + 96*x^68 + 124*x^67 + 96*x^66 + 89*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 118*x^5 + 96*x^4 + 60*x^3 + 96*x^2 + 65*x + 32, x^73 + 60*x^71 + 32*x^70 + 38*x^69 + 112*x^68 + 92*x^67 + 64*x^66 + 73*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 38*x^5 + 112*x^4 + 28*x^3 + 64*x^2 + 49*x + 48, x^73 + 60*x^71 + 40*x^70 + 54*x^69 + 56*x^68 + 60*x^67 + 24*x^66 + 89*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 54*x^5 + 56*x^4 + 124*x^3 + 24*x^2 + 65*x + 8, x^73 + 60*x^71 + 80*x^70 + 54*x^69 + 16*x^68 + 124*x^67 + 112*x^66 + 25*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 54*x^5 + 16*x^4 + 60*x^3 + 112*x^2 + x + 48, x^73 + 60*x^71 + 88*x^70 + 54*x^69 + 104*x^68 + 124*x^67 + 104*x^66 + 25*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 54*x^5 + 104*x^4 + 60*x^3 + 104*x^2 + x + 88, x^73 + 60*x^71 + 8*x^70 + 6*x^69 + 104*x^68 + 28*x^67 + 88*x^66 + 41*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 6*x^5 + 104*x^4 + 92*x^3 + 88*x^2 + 17*x + 56, x^73 + 60*x^71 + 52*x^70 + 62*x^69 + 108*x^68 + 44*x^67 + 12*x^66 + 97*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 62*x^5 + 44*x^4 + 108*x^3 + 76*x^2 + 73*x + 20, x^73 + 60*x^71 + 80*x^70 + 22*x^69 + 80*x^68 + 60*x^67 + 112*x^66 + 121*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 22*x^5 + 80*x^4 + 124*x^3 + 112*x^2 + 97*x + 112, x^73 + 60*x^71 + 116*x^70 + 46*x^69 + 60*x^68 + 76*x^67 + 108*x^66 + 81*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 46*x^5 + 124*x^4 + 12*x^3 + 44*x^2 + 57*x + 36, x^73 + 60*x^71 + 12*x^70 + 110*x^69 + 4*x^68 + 76*x^67 + 20*x^66 + 17*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 110*x^5 + 68*x^4 + 12*x^3 + 84*x^2 + 121*x + 28, x^73 + 60*x^71 + 64*x^70 + 22*x^69 + 96*x^68 + 124*x^67 + 64*x^66 + 57*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 22*x^5 + 96*x^4 + 60*x^3 + 64*x^2 + 33*x + 32, x^73 + 60*x^71 + 72*x^70 + 118*x^69 + 24*x^68 + 124*x^67 + 56*x^66 + 89*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 118*x^5 + 24*x^4 + 60*x^3 + 56*x^2 + 65*x + 104, x^73 + 60*x^71 + 8*x^70 + 22*x^69 + 56*x^68 + 60*x^67 + 56*x^66 + 121*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 22*x^5 + 56*x^4 + 124*x^3 + 56*x^2 + 97*x + 8, x^73 + 60*x^71 + 112*x^70 + 38*x^69 + 96*x^68 + 28*x^67 + 48*x^66 + 9*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 38*x^5 + 96*x^4 + 92*x^3 + 48*x^2 + 113*x, x^73 + 60*x^71 + 60*x^70 + 30*x^69 + 36*x^68 + 44*x^67 + 68*x^66 + x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 30*x^5 + 100*x^4 + 108*x^3 + 4*x^2 + 105*x + 28, x^73 + 60*x^71 + 48*x^70 + 70*x^69 + 92*x^67 + 48*x^66 + 41*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 70*x^5 + 28*x^3 + 48*x^2 + 17*x + 32, x^73 + 60*x^71 + 32*x^70 + 118*x^69 + 96*x^68 + 60*x^67 + 32*x^66 + 25*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 118*x^5 + 96*x^4 + 124*x^3 + 32*x^2 + x + 96, x^73 + 60*x^71 + 32*x^70 + 102*x^69 + 16*x^68 + 28*x^67 + 64*x^66 + 73*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 96*x^36 + 104*x^35 + 14*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 102*x^5 + 16*x^4 + 92*x^3 + 64*x^2 + 49*x + 16, x^73 + 60*x^71 + 108*x^70 + 94*x^69 + 116*x^68 + 44*x^67 + 20*x^66 + 65*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 94*x^5 + 52*x^4 + 108*x^3 + 84*x^2 + 41*x + 76, x^73 + 60*x^71 + 12*x^70 + 110*x^69 + 4*x^68 + 12*x^67 + 84*x^66 + 81*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 110*x^5 + 68*x^4 + 76*x^3 + 20*x^2 + 57*x + 92, x^73 + 60*x^71 + 100*x^70 + 110*x^69 + 108*x^68 + 12*x^67 + 124*x^66 + 81*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 110*x^5 + 44*x^4 + 76*x^3 + 60*x^2 + 57*x + 116, x^73 + 60*x^71 + 20*x^70 + 30*x^69 + 76*x^68 + 108*x^67 + 44*x^66 + 65*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 30*x^5 + 12*x^4 + 44*x^3 + 108*x^2 + 41*x + 52, x^73 + 60*x^71 + 88*x^70 + 54*x^69 + 72*x^68 + 60*x^67 + 104*x^66 + 89*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 54*x^5 + 72*x^4 + 124*x^3 + 104*x^2 + 65*x + 120, x^73 + 60*x^71 + 4*x^70 + 14*x^69 + 108*x^68 + 76*x^67 + 28*x^66 + 113*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 14*x^5 + 44*x^4 + 12*x^3 + 92*x^2 + 89*x + 52, x^73 + 60*x^71 + 28*x^70 + 94*x^69 + 36*x^68 + 44*x^67 + 36*x^66 + 65*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 94*x^5 + 100*x^4 + 108*x^3 + 100*x^2 + 41*x + 92, x^73 + 60*x^71 + 28*x^70 + 110*x^69 + 116*x^68 + 12*x^67 + 68*x^66 + 81*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 110*x^5 + 52*x^4 + 76*x^3 + 4*x^2 + 57*x + 108, x^73 + 60*x^71 + 8*x^70 + 118*x^69 + 88*x^68 + 60*x^67 + 56*x^66 + 25*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 118*x^5 + 88*x^4 + 124*x^3 + 56*x^2 + x + 104, x^73 + 60*x^71 + 48*x^70 + 70*x^69 + 64*x^68 + 92*x^67 + 48*x^66 + 41*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 104*x^35 + 32*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 70*x^5 + 64*x^4 + 28*x^3 + 48*x^2 + 17*x + 96, x^73 + 60*x^71 + 56*x^70 + 86*x^69 + 8*x^68 + 124*x^67 + 72*x^66 + 121*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 48*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 86*x^5 + 8*x^4 + 60*x^3 + 72*x^2 + 97*x + 120, x^73 + 60*x^71 + 124*x^70 + 110*x^69 + 20*x^68 + 76*x^67 + 36*x^66 + 17*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 110*x^5 + 84*x^4 + 12*x^3 + 100*x^2 + 121*x + 12, x^73 + 60*x^71 + 72*x^70 + 54*x^69 + 120*x^68 + 60*x^67 + 56*x^66 + 89*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 54*x^5 + 120*x^4 + 124*x^3 + 56*x^2 + 65*x + 8, x^73 + 60*x^71 + 24*x^70 + 38*x^69 + 56*x^68 + 92*x^67 + 8*x^66 + 73*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 38*x^5 + 56*x^4 + 28*x^3 + 8*x^2 + 49*x + 40, x^73 + 60*x^71 + 108*x^70 + 62*x^69 + 116*x^68 + 108*x^67 + 20*x^66 + 33*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 62*x^5 + 52*x^4 + 44*x^3 + 84*x^2 + 9*x + 76, x^73 + 60*x^71 + 32*x^70 + 38*x^69 + 48*x^68 + 28*x^67 + 9*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 100*x^37 + 32*x^36 + 104*x^35 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 38*x^5 + 48*x^4 + 92*x^3 + 113*x + 48, x^73 + 60*x^71 + 56*x^70 + 70*x^69 + 56*x^68 + 28*x^67 + 40*x^66 + 105*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 70*x^5 + 56*x^4 + 92*x^3 + 40*x^2 + 81*x + 104, x^73 + 60*x^71 + 16*x^70 + 102*x^69 + 32*x^68 + 28*x^67 + 80*x^66 + 73*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 102*x^5 + 32*x^4 + 92*x^3 + 80*x^2 + 49*x, x^73 + 60*x^71 + 84*x^70 + 110*x^69 + 124*x^68 + 76*x^67 + 76*x^66 + 17*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 110*x^5 + 60*x^4 + 12*x^3 + 12*x^2 + 121*x + 36, x^73 + 60*x^71 + 108*x^70 + 14*x^69 + 4*x^68 + 76*x^67 + 52*x^66 + 113*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 14*x^5 + 68*x^4 + 12*x^3 + 116*x^2 + 89*x + 28, x^73 + 60*x^71 + 104*x^70 + 6*x^69 + 72*x^68 + 92*x^67 + 56*x^66 + 105*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 6*x^5 + 72*x^4 + 28*x^3 + 56*x^2 + 81*x + 24, x^73 + 60*x^71 + 24*x^70 + 38*x^69 + 120*x^68 + 28*x^67 + 72*x^66 + 9*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 24*x^6 + 38*x^5 + 120*x^4 + 92*x^3 + 72*x^2 + 113*x + 40, x^73 + 60*x^71 + 28*x^70 + 30*x^69 + 36*x^68 + 44*x^67 + 36*x^66 + x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 30*x^5 + 100*x^4 + 108*x^3 + 100*x^2 + 105*x + 92, x^73 + 60*x^71 + 8*x^70 + 22*x^69 + 24*x^68 + 124*x^67 + 56*x^66 + 57*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 22*x^5 + 24*x^4 + 60*x^3 + 56*x^2 + 33*x + 40, x^73 + 60*x^71 + 52*x^70 + 62*x^69 + 76*x^68 + 108*x^67 + 12*x^66 + 33*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 8*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 62*x^5 + 12*x^4 + 44*x^3 + 76*x^2 + 9*x + 52, x^73 + 60*x^71 + 76*x^70 + 78*x^69 + 36*x^68 + 76*x^67 + 84*x^66 + 49*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 78*x^5 + 100*x^4 + 12*x^3 + 20*x^2 + 25*x + 124, x^73 + 60*x^71 + 54*x^69 + 32*x^68 + 124*x^67 + 64*x^66 + 25*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 64*x^36 + 40*x^35 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 54*x^5 + 32*x^4 + 60*x^3 + 64*x^2 + x + 32, x^73 + 60*x^71 + 40*x^70 + 22*x^69 + 56*x^68 + 60*x^67 + 88*x^66 + 121*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 22*x^5 + 56*x^4 + 124*x^3 + 88*x^2 + 97*x + 72, x^73 + 60*x^71 + 8*x^70 + 54*x^69 + 24*x^68 + 124*x^67 + 120*x^66 + 25*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 54*x^5 + 24*x^4 + 60*x^3 + 120*x^2 + x + 104, x^73 + 60*x^71 + 100*x^70 + 94*x^69 + 124*x^68 + 44*x^67 + 28*x^66 + 65*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 94*x^5 + 60*x^4 + 108*x^3 + 92*x^2 + 41*x + 68, x^73 + 60*x^71 + 20*x^70 + 14*x^69 + 124*x^68 + 76*x^67 + 76*x^66 + 113*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 84*x^6 + 14*x^5 + 60*x^4 + 12*x^3 + 12*x^2 + 89*x + 100, x^73 + 60*x^71 + 60*x^70 + 14*x^69 + 116*x^68 + 76*x^67 + 100*x^66 + 113*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 120*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 14*x^5 + 52*x^4 + 12*x^3 + 36*x^2 + 89*x + 44, x^73 + 60*x^71 + 48*x^70 + 6*x^69 + 96*x^68 + 28*x^67 + 48*x^66 + 41*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 6*x^5 + 96*x^4 + 92*x^3 + 48*x^2 + 17*x + 64, x^73 + 60*x^71 + 52*x^70 + 14*x^69 + 124*x^68 + 76*x^67 + 108*x^66 + 113*x^65 + 100*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 40*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 14*x^5 + 60*x^4 + 12*x^3 + 44*x^2 + 89*x + 36, x^73 + 60*x^71 + 92*x^70 + 110*x^69 + 20*x^68 + 76*x^67 + 4*x^66 + 17*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 110*x^5 + 84*x^4 + 12*x^3 + 68*x^2 + 121*x + 76, x^73 + 60*x^71 + 40*x^70 + 118*x^69 + 24*x^68 + 60*x^67 + 88*x^66 + 25*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 118*x^5 + 24*x^4 + 124*x^3 + 88*x^2 + x + 104, x^73 + 60*x^71 + 40*x^70 + 86*x^69 + 24*x^68 + 124*x^67 + 88*x^66 + 121*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 86*x^5 + 24*x^4 + 60*x^3 + 88*x^2 + 97*x + 104, x^73 + 60*x^71 + 60*x^70 + 126*x^69 + 68*x^68 + 108*x^67 + 4*x^66 + 97*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 126*x^5 + 4*x^4 + 44*x^3 + 68*x^2 + 73*x + 60, x^73 + 60*x^71 + 72*x^70 + 54*x^69 + 88*x^68 + 124*x^67 + 56*x^66 + 25*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 54*x^5 + 88*x^4 + 60*x^3 + 56*x^2 + x + 40, x^73 + 60*x^71 + 80*x^70 + 6*x^69 + 28*x^67 + 16*x^66 + 41*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 6*x^5 + 92*x^3 + 16*x^2 + 17*x + 32, x^73 + 60*x^71 + 108*x^70 + 14*x^69 + 100*x^68 + 76*x^67 + 116*x^66 + 113*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 14*x^5 + 36*x^4 + 12*x^3 + 52*x^2 + 89*x + 124, x^73 + 60*x^71 + 88*x^70 + 54*x^69 + 40*x^68 + 60*x^67 + 40*x^66 + 89*x^65 + 88*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 54*x^5 + 40*x^4 + 124*x^3 + 40*x^2 + 65*x + 88, x^73 + 60*x^71 + 72*x^70 + 86*x^69 + 24*x^68 + 60*x^67 + 56*x^66 + 57*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 16*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 86*x^5 + 24*x^4 + 124*x^3 + 56*x^2 + 33*x + 104, x^73 + 60*x^71 + 84*x^70 + 94*x^69 + 108*x^68 + 44*x^67 + 108*x^66 + 65*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 94*x^5 + 44*x^4 + 108*x^3 + 44*x^2 + 41*x + 20, x^73 + 60*x^71 + 64*x^70 + 6*x^69 + 16*x^68 + 92*x^67 + 96*x^66 + 105*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 6*x^5 + 16*x^4 + 28*x^3 + 96*x^2 + 81*x + 80, x^73 + 60*x^71 + 72*x^70 + 22*x^69 + 56*x^68 + 60*x^67 + 120*x^66 + 121*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 22*x^5 + 56*x^4 + 124*x^3 + 120*x^2 + 97*x + 8, x^73 + 60*x^71 + 68*x^70 + 126*x^69 + 60*x^68 + 44*x^67 + 60*x^66 + 33*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 126*x^5 + 124*x^4 + 108*x^3 + 124*x^2 + 9*x + 4, x^73 + 60*x^71 + 72*x^70 + 102*x^69 + 8*x^68 + 28*x^67 + 24*x^66 + 73*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 48*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 102*x^5 + 8*x^4 + 92*x^3 + 24*x^2 + 49*x + 24, x^73 + 60*x^71 + 8*x^70 + 102*x^69 + 104*x^68 + 92*x^67 + 88*x^66 + 9*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 102*x^5 + 104*x^4 + 28*x^3 + 88*x^2 + 113*x + 56, x^73 + 60*x^71 + 4*x^70 + 110*x^69 + 44*x^68 + 12*x^67 + 28*x^66 + 81*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 20*x^37 + 72*x^36 + 8*x^35 + 104*x^34 + 62*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 68*x^6 + 110*x^5 + 108*x^4 + 76*x^3 + 92*x^2 + 57*x + 116, x^73 + 60*x^71 + 16*x^70 + 6*x^69 + 64*x^68 + 28*x^67 + 80*x^66 + 41*x^65 + 96*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 6*x^5 + 64*x^4 + 92*x^3 + 80*x^2 + 17*x + 96, x^73 + 60*x^71 + 60*x^70 + 78*x^69 + 84*x^68 + 12*x^67 + 100*x^66 + 113*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 124*x^6 + 78*x^5 + 20*x^4 + 76*x^3 + 36*x^2 + 89*x + 76, x^73 + 60*x^71 + 100*x^70 + 94*x^69 + 28*x^68 + 44*x^67 + 92*x^66 + 65*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 94*x^5 + 92*x^4 + 108*x^3 + 28*x^2 + 41*x + 100, x^73 + 60*x^71 + 56*x^70 + 118*x^69 + 104*x^68 + 124*x^67 + 72*x^66 + 89*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 68*x^37 + 112*x^36 + 40*x^35 + 48*x^34 + 110*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 56*x^6 + 118*x^5 + 104*x^4 + 60*x^3 + 72*x^2 + 65*x + 24, x^73 + 60*x^71 + 16*x^70 + 22*x^69 + 80*x^68 + 124*x^67 + 112*x^66 + 57*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 4*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 46*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 22*x^5 + 80*x^4 + 60*x^3 + 112*x^2 + 33*x + 48, x^73 + 60*x^71 + 72*x^70 + 54*x^69 + 56*x^68 + 60*x^67 + 56*x^66 + 89*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 54*x^5 + 56*x^4 + 124*x^3 + 56*x^2 + 65*x + 72, x^73 + 60*x^71 + 88*x^70 + 86*x^69 + 104*x^68 + 124*x^67 + 40*x^66 + 121*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 112*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 86*x^5 + 104*x^4 + 60*x^3 + 40*x^2 + 97*x + 24, x^73 + 60*x^71 + 108*x^70 + 126*x^69 + 84*x^68 + 108*x^67 + 84*x^66 + 97*x^65 + 108*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 56*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 126*x^5 + 20*x^4 + 44*x^3 + 20*x^2 + 73*x + 44, x^73 + 60*x^71 + 100*x^70 + 110*x^69 + 76*x^68 + 76*x^67 + 124*x^66 + 17*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 110*x^5 + 12*x^4 + 12*x^3 + 60*x^2 + 121*x + 20, x^73 + 60*x^71 + 16*x^70 + 102*x^69 + 96*x^68 + 28*x^67 + 80*x^66 + 73*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 102*x^5 + 96*x^4 + 92*x^3 + 80*x^2 + 49*x + 64, x^73 + 60*x^71 + 104*x^70 + 6*x^69 + 8*x^68 + 28*x^67 + 120*x^66 + 41*x^65 + 24*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 36*x^37 + 48*x^36 + 104*x^35 + 80*x^34 + 78*x^33 + 16*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 104*x^6 + 6*x^5 + 8*x^4 + 92*x^3 + 120*x^2 + 17*x + 24, x^73 + 60*x^71 + 124*x^70 + 94*x^69 + 36*x^68 + 108*x^67 + 68*x^66 + x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 94*x^5 + 100*x^4 + 44*x^3 + 4*x^2 + 105*x + 92, x^73 + 60*x^71 + 88*x^70 + 70*x^69 + 120*x^68 + 28*x^67 + 72*x^66 + 105*x^65 + 104*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 36*x^37 + 80*x^36 + 104*x^35 + 48*x^34 + 78*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 70*x^5 + 120*x^4 + 92*x^3 + 72*x^2 + 81*x + 104, x^73 + 60*x^71 + 84*x^70 + 62*x^69 + 12*x^68 + 108*x^67 + 44*x^66 + 33*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 116*x^37 + 8*x^36 + 72*x^35 + 72*x^34 + 30*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 62*x^5 + 76*x^4 + 44*x^3 + 108*x^2 + 9*x + 52, x^73 + 60*x^71 + 96*x^70 + 6*x^69 + 112*x^68 + 92*x^67 + 64*x^66 + 105*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 6*x^5 + 112*x^4 + 28*x^3 + 64*x^2 + 81*x + 112, x^73 + 60*x^71 + 22*x^69 + 32*x^68 + 60*x^67 + 64*x^66 + 121*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 22*x^5 + 32*x^4 + 124*x^3 + 64*x^2 + 97*x + 32, x^73 + 60*x^71 + 64*x^70 + 22*x^69 + 32*x^68 + 60*x^67 + 121*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 64*x^36 + 40*x^35 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 22*x^5 + 32*x^4 + 124*x^3 + 97*x + 32, x^73 + 60*x^71 + 54*x^69 + 124*x^67 + 25*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 68*x^37 + 40*x^35 + 110*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 54*x^5 + 60*x^3 + x, x^73 + 60*x^71 + 36*x^70 + 126*x^69 + 92*x^68 + 44*x^67 + 92*x^66 + 33*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 126*x^5 + 28*x^4 + 108*x^3 + 28*x^2 + 9*x + 100, x^73 + 60*x^71 + 112*x^70 + 6*x^69 + 32*x^68 + 92*x^67 + 48*x^66 + 105*x^65 + 64*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 36*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 78*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 6*x^5 + 32*x^4 + 28*x^3 + 48*x^2 + 81*x + 64, x^73 + 60*x^71 + 100*x^70 + 14*x^69 + 76*x^68 + 76*x^67 + 60*x^66 + 113*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 14*x^5 + 12*x^4 + 12*x^3 + 124*x^2 + 89*x + 84, x^73 + 60*x^71 + 16*x^70 + 118*x^69 + 80*x^68 + 60*x^67 + 112*x^66 + 25*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 68*x^37 + 96*x^36 + 40*x^35 + 32*x^34 + 110*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 118*x^5 + 80*x^4 + 124*x^3 + 112*x^2 + x + 48, x^73 + 60*x^71 + 84*x^70 + 78*x^69 + 28*x^68 + 76*x^67 + 76*x^66 + 49*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 8*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 78*x^5 + 92*x^4 + 12*x^3 + 12*x^2 + 25*x + 4, x^73 + 60*x^71 + 68*x^70 + 62*x^69 + 92*x^68 + 108*x^67 + 60*x^66 + 33*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 116*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 30*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 62*x^5 + 28*x^4 + 44*x^3 + 124*x^2 + 9*x + 100, x^73 + 60*x^71 + 120*x^70 + 38*x^69 + 120*x^68 + 92*x^67 + 104*x^66 + 73*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 80*x^38 + 100*x^37 + 80*x^36 + 104*x^35 + 112*x^34 + 14*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 120*x^6 + 38*x^5 + 120*x^4 + 28*x^3 + 104*x^2 + 49*x + 40, x^73 + 60*x^71 + 36*x^70 + 94*x^69 + 124*x^68 + 108*x^67 + 28*x^66 + x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 52*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 94*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 94*x^5 + 60*x^4 + 44*x^3 + 92*x^2 + 105*x + 4, x^73 + 60*x^71 + 48*x^70 + 54*x^69 + 112*x^68 + 124*x^67 + 16*x^66 + 25*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 68*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 110*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 54*x^5 + 112*x^4 + 60*x^3 + 16*x^2 + x + 80, x^73 + 60*x^71 + 96*x^70 + 70*x^69 + 80*x^68 + 92*x^67 + 41*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 70*x^5 + 80*x^4 + 28*x^3 + 17*x + 80, x^73 + 60*x^71 + 96*x^70 + 54*x^69 + 96*x^68 + 124*x^67 + 32*x^66 + 25*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 68*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 110*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 54*x^5 + 96*x^4 + 60*x^3 + 32*x^2 + x + 32, x^73 + 60*x^71 + 64*x^70 + 6*x^69 + 80*x^68 + 92*x^67 + 96*x^66 + 105*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 96*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 6*x^5 + 80*x^4 + 28*x^3 + 96*x^2 + 81*x + 16, x^73 + 60*x^71 + 108*x^70 + 14*x^69 + 100*x^68 + 12*x^67 + 52*x^66 + 49*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 44*x^6 + 14*x^5 + 36*x^4 + 76*x^3 + 116*x^2 + 25*x + 60, x^73 + 60*x^71 + 96*x^70 + 6*x^69 + 112*x^68 + 28*x^67 + 41*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 32*x^36 + 104*x^35 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 6*x^5 + 112*x^4 + 92*x^3 + 17*x + 48, x^73 + 60*x^71 + 68*x^70 + 94*x^69 + 28*x^68 + 108*x^67 + 124*x^66 + x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 88*x^38 + 52*x^37 + 104*x^36 + 72*x^35 + 40*x^34 + 94*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 4*x^6 + 94*x^5 + 92*x^4 + 44*x^3 + 60*x^2 + 105*x + 100, x^73 + 60*x^71 + 44*x^70 + 78*x^69 + 36*x^68 + 12*x^67 + 116*x^66 + 113*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 84*x^37 + 24*x^36 + 8*x^35 + 120*x^34 + 126*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 78*x^5 + 100*x^4 + 76*x^3 + 52*x^2 + 89*x + 124, x^73 + 60*x^71 + 100*x^70 + 46*x^69 + 76*x^68 + 76*x^67 + 124*x^66 + 81*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 46*x^5 + 12*x^4 + 12*x^3 + 60*x^2 + 57*x + 20, x^73 + 60*x^71 + 88*x^70 + 22*x^69 + 72*x^68 + 60*x^67 + 40*x^66 + 121*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 22*x^5 + 72*x^4 + 124*x^3 + 40*x^2 + 97*x + 56, x^73 + 60*x^71 + 92*x^70 + 46*x^69 + 116*x^68 + 12*x^67 + 4*x^66 + 17*x^65 + 44*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 20*x^37 + 120*x^36 + 8*x^35 + 88*x^34 + 62*x^33 + 72*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 46*x^5 + 52*x^4 + 76*x^3 + 68*x^2 + 121*x + 108, x^73 + 60*x^71 + 76*x^70 + 30*x^69 + 52*x^68 + 44*x^67 + 116*x^66 + x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 52*x^37 + 120*x^36 + 72*x^35 + 120*x^34 + 94*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 30*x^5 + 116*x^4 + 108*x^3 + 52*x^2 + 105*x + 76, x^73 + 60*x^71 + 92*x^70 + 78*x^69 + 20*x^68 + 12*x^67 + 4*x^66 + 113*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 78*x^5 + 84*x^4 + 76*x^3 + 68*x^2 + 89*x + 76, x^73 + 60*x^71 + 124*x^70 + 78*x^69 + 20*x^68 + 12*x^67 + 36*x^66 + 113*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 78*x^5 + 84*x^4 + 76*x^3 + 100*x^2 + 89*x + 12, x^73 + 60*x^71 + 40*x^70 + 118*x^69 + 56*x^68 + 124*x^67 + 88*x^66 + 89*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 118*x^5 + 56*x^4 + 60*x^3 + 88*x^2 + 65*x + 72, x^73 + 60*x^71 + 48*x^70 + 102*x^69 + 64*x^68 + 92*x^67 + 112*x^66 + 9*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 104*x^35 + 32*x^34 + 14*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 102*x^5 + 64*x^4 + 28*x^3 + 112*x^2 + 113*x + 32, x^73 + 60*x^71 + 124*x^70 + 46*x^69 + 20*x^68 + 76*x^67 + 36*x^66 + 81*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 20*x^37 + 56*x^36 + 8*x^35 + 24*x^34 + 62*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 46*x^5 + 84*x^4 + 12*x^3 + 100*x^2 + 57*x + 12, x^73 + 60*x^71 + 38*x^69 + 48*x^68 + 92*x^67 + 32*x^66 + 73*x^65 + 48*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 100*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 14*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 38*x^5 + 48*x^4 + 28*x^3 + 32*x^2 + 49*x + 48, x^73 + 60*x^71 + 84*x^70 + 46*x^69 + 124*x^68 + 12*x^67 + 12*x^66 + 17*x^65 + 36*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 20*x^37 + 40*x^36 + 8*x^35 + 8*x^34 + 62*x^33 + 24*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 46*x^5 + 60*x^4 + 76*x^3 + 76*x^2 + 121*x + 100, x^73 + 60*x^71 + 8*x^70 + 118*x^69 + 120*x^68 + 124*x^67 + 56*x^66 + 89*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 68*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 110*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 118*x^5 + 120*x^4 + 60*x^3 + 56*x^2 + 65*x + 72, x^73 + 60*x^71 + 44*x^70 + 126*x^69 + 52*x^68 + 108*x^67 + 84*x^66 + 97*x^65 + 76*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 72*x^53 + 112*x^52 + 16*x^51 + 112*x^50 + 100*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 72*x^38 + 116*x^37 + 120*x^36 + 72*x^35 + 56*x^34 + 30*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 72*x^21 + 112*x^20 + 16*x^19 + 112*x^18 + 84*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 108*x^6 + 126*x^5 + 116*x^4 + 44*x^3 + 20*x^2 + 73*x + 12, x^73 + 60*x^71 + 100*x^70 + 78*x^69 + 44*x^68 + 76*x^67 + 124*x^66 + 49*x^65 + 116*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 78*x^5 + 108*x^4 + 12*x^3 + 60*x^2 + 25*x + 52, x^73 + 60*x^71 + 12*x^70 + 46*x^69 + 4*x^68 + 12*x^67 + 84*x^66 + 17*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 46*x^5 + 68*x^4 + 76*x^3 + 20*x^2 + 121*x + 92, x^73 + 60*x^71 + 76*x^70 + 78*x^69 + 4*x^68 + 76*x^67 + 20*x^66 + 49*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 78*x^5 + 68*x^4 + 12*x^3 + 84*x^2 + 25*x + 92, x^73 + 60*x^71 + 88*x^70 + 38*x^69 + 88*x^68 + 92*x^67 + 8*x^66 + 73*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 38*x^5 + 88*x^4 + 28*x^3 + 8*x^2 + 49*x + 72, x^73 + 60*x^71 + 124*x^70 + 126*x^69 + 36*x^68 + 108*x^67 + 4*x^66 + 97*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 88*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 126*x^5 + 100*x^4 + 44*x^3 + 68*x^2 + 73*x + 28, x^73 + 60*x^71 + 64*x^70 + 70*x^69 + 112*x^68 + 28*x^67 + 96*x^66 + 105*x^65 + 112*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 36*x^37 + 32*x^36 + 104*x^35 + 64*x^34 + 78*x^33 + 32*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 64*x^6 + 70*x^5 + 112*x^4 + 92*x^3 + 96*x^2 + 81*x + 112, x^73 + 60*x^71 + 116*x^70 + 94*x^69 + 108*x^68 + 44*x^67 + 12*x^66 + 65*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 94*x^5 + 44*x^4 + 108*x^3 + 76*x^2 + 41*x + 84, x^73 + 60*x^71 + 48*x^70 + 38*x^69 + 96*x^68 + 28*x^67 + 112*x^66 + 9*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 32*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 48*x^6 + 38*x^5 + 96*x^4 + 92*x^3 + 112*x^2 + 113*x, x^73 + 60*x^71 + 36*x^70 + 110*x^69 + 76*x^68 + 12*x^67 + 124*x^66 + 81*x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 20*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 62*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 110*x^5 + 12*x^4 + 76*x^3 + 60*x^2 + 57*x + 84, x^73 + 60*x^71 + 52*x^70 + 14*x^69 + 92*x^68 + 12*x^67 + 108*x^66 + 49*x^65 + 4*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 84*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 126*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 14*x^5 + 28*x^4 + 76*x^3 + 44*x^2 + 25*x + 68, x^73 + 60*x^71 + 88*x^70 + 102*x^69 + 88*x^68 + 28*x^67 + 72*x^66 + 73*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 40*x^53 + 32*x^52 + 80*x^51 + 96*x^50 + 68*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 100*x^37 + 16*x^36 + 104*x^35 + 48*x^34 + 14*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 40*x^21 + 32*x^20 + 80*x^19 + 96*x^18 + 52*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 102*x^5 + 88*x^4 + 92*x^3 + 72*x^2 + 49*x + 8, x^73 + 60*x^71 + 22*x^69 + 60*x^67 + 121*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 4*x^37 + 40*x^35 + 46*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 22*x^5 + 124*x^3 + 97*x, x^73 + 60*x^71 + 28*x^70 + 126*x^69 + 36*x^68 + 44*x^67 + 100*x^66 + 33*x^65 + 92*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 116*x^37 + 24*x^36 + 72*x^35 + 24*x^34 + 30*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 92*x^6 + 126*x^5 + 100*x^4 + 108*x^3 + 36*x^2 + 9*x + 28, x^73 + 60*x^71 + 100*x^70 + 78*x^69 + 76*x^68 + 12*x^67 + 124*x^66 + 113*x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 8*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 78*x^5 + 12*x^4 + 76*x^3 + 60*x^2 + 89*x + 20, x^73 + 60*x^71 + 52*x^70 + 110*x^69 + 28*x^68 + 76*x^67 + 108*x^66 + 17*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 8*x^53 + 80*x^52 + 16*x^51 + 16*x^50 + 36*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 20*x^37 + 104*x^36 + 8*x^35 + 72*x^34 + 62*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 8*x^21 + 80*x^20 + 16*x^19 + 16*x^18 + 20*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 116*x^6 + 110*x^5 + 92*x^4 + 12*x^3 + 44*x^2 + 121*x + 4, x^73 + 60*x^71 + 84*x^70 + 94*x^69 + 44*x^68 + 108*x^67 + 44*x^66 + x^65 + 84*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 56*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 72*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 20*x^6 + 94*x^5 + 108*x^4 + 44*x^3 + 108*x^2 + 105*x + 20, x^73 + 60*x^71 + 36*x^70 + 14*x^69 + 108*x^68 + 76*x^67 + 60*x^66 + 113*x^65 + 52*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 8*x^53 + 16*x^52 + 16*x^51 + 80*x^50 + 36*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 84*x^37 + 72*x^36 + 8*x^35 + 40*x^34 + 126*x^33 + 120*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 8*x^21 + 16*x^20 + 16*x^19 + 80*x^18 + 20*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 14*x^5 + 44*x^4 + 12*x^3 + 124*x^2 + 89*x + 116, x^73 + 60*x^71 + 40*x^70 + 54*x^69 + 88*x^68 + 60*x^67 + 88*x^66 + 89*x^65 + 40*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 112*x^38 + 68*x^37 + 16*x^36 + 40*x^35 + 16*x^34 + 110*x^33 + 112*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 40*x^6 + 54*x^5 + 88*x^4 + 124*x^3 + 88*x^2 + 65*x + 40, x^73 + 60*x^71 + 80*x^70 + 102*x^69 + 32*x^68 + 28*x^67 + 16*x^66 + 73*x^65 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 100*x^37 + 64*x^36 + 104*x^35 + 96*x^34 + 14*x^33 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 80*x^6 + 102*x^5 + 32*x^4 + 92*x^3 + 16*x^2 + 49*x, x^73 + 60*x^71 + 76*x^70 + 110*x^69 + 36*x^68 + 76*x^67 + 20*x^66 + 17*x^65 + 124*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 20*x^37 + 24*x^36 + 8*x^35 + 56*x^34 + 62*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 12*x^6 + 110*x^5 + 100*x^4 + 12*x^3 + 84*x^2 + 121*x + 60, x^73 + 60*x^71 + 116*x^70 + 30*x^69 + 108*x^68 + 44*x^67 + 12*x^66 + x^65 + 20*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 112*x^54 + 72*x^53 + 16*x^52 + 16*x^51 + 16*x^50 + 100*x^49 + 112*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 120*x^38 + 52*x^37 + 72*x^36 + 72*x^35 + 8*x^34 + 94*x^33 + 56*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 112*x^22 + 72*x^21 + 16*x^20 + 16*x^19 + 16*x^18 + 84*x^17 + 112*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 52*x^6 + 30*x^5 + 44*x^4 + 108*x^3 + 76*x^2 + 105*x + 84, x^73 + 60*x^71 + 32*x^70 + 22*x^69 + 96*x^68 + 60*x^67 + 96*x^66 + 121*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 104*x^53 + 80*x^51 + 4*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 4*x^37 + 64*x^36 + 40*x^35 + 64*x^34 + 46*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 104*x^21 + 80*x^19 + 116*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 32*x^6 + 22*x^5 + 96*x^4 + 124*x^3 + 96*x^2 + 97*x + 32, x^73 + 60*x^71 + 96*x^70 + 70*x^69 + 80*x^68 + 28*x^67 + 64*x^66 + 105*x^65 + 16*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 40*x^53 + 64*x^52 + 80*x^51 + 68*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 64*x^38 + 36*x^37 + 96*x^36 + 104*x^35 + 78*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 40*x^21 + 64*x^20 + 80*x^19 + 52*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 96*x^6 + 70*x^5 + 80*x^4 + 92*x^3 + 64*x^2 + 81*x + 16, x^73 + 60*x^71 + 8*x^70 + 6*x^69 + 40*x^68 + 92*x^67 + 24*x^66 + 105*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 6*x^5 + 40*x^4 + 28*x^3 + 24*x^2 + 81*x + 56, x^73 + 60*x^71 + 12*x^70 + 14*x^69 + 4*x^68 + 76*x^67 + 84*x^66 + 113*x^65 + 28*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 16*x^54 + 8*x^53 + 48*x^52 + 16*x^51 + 112*x^50 + 36*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 8*x^38 + 84*x^37 + 88*x^36 + 8*x^35 + 56*x^34 + 126*x^33 + 104*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 16*x^22 + 8*x^21 + 48*x^20 + 16*x^19 + 112*x^18 + 20*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 76*x^6 + 14*x^5 + 68*x^4 + 12*x^3 + 20*x^2 + 89*x + 92, x^73 + 60*x^71 + 8*x^70 + 86*x^69 + 120*x^68 + 124*x^67 + 120*x^66 + 121*x^65 + 8*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 8*x^6 + 86*x^5 + 120*x^4 + 60*x^3 + 120*x^2 + 97*x + 8, x^73 + 60*x^71 + 16*x^70 + 6*x^69 + 64*x^68 + 92*x^67 + 16*x^66 + 105*x^65 + 32*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 40*x^53 + 80*x^51 + 64*x^50 + 68*x^49 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 96*x^38 + 36*x^37 + 104*x^35 + 96*x^34 + 78*x^33 + 64*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 40*x^21 + 80*x^19 + 64*x^18 + 52*x^17 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 16*x^6 + 6*x^5 + 64*x^4 + 28*x^3 + 16*x^2 + 81*x + 32, x^73 + 60*x^71 + 92*x^70 + 78*x^69 + 84*x^68 + 76*x^67 + 68*x^66 + 49*x^65 + 12*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 8*x^53 + 112*x^52 + 16*x^51 + 48*x^50 + 36*x^49 + 16*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 104*x^38 + 84*x^37 + 56*x^36 + 8*x^35 + 88*x^34 + 126*x^33 + 8*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 8*x^21 + 112*x^20 + 16*x^19 + 48*x^18 + 20*x^17 + 16*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 28*x^6 + 78*x^5 + 20*x^4 + 12*x^3 + 4*x^2 + 25*x + 76, x^73 + 60*x^71 + 112*x^70 + 86*x^69 + 112*x^68 + 60*x^67 + 80*x^66 + 57*x^65 + 80*x^64 + 96*x^63 + 16*x^61 + 96*x^59 + 116*x^57 + 80*x^55 + 64*x^54 + 104*x^53 + 64*x^52 + 80*x^51 + 64*x^50 + 4*x^49 + 64*x^48 + 32*x^47 + 112*x^45 + 32*x^43 + 110*x^41 + 40*x^39 + 32*x^38 + 4*x^37 + 32*x^36 + 40*x^35 + 96*x^34 + 46*x^33 + 96*x^32 + 32*x^31 + 112*x^29 + 32*x^27 + 4*x^25 + 80*x^23 + 64*x^22 + 104*x^21 + 64*x^20 + 80*x^19 + 64*x^18 + 116*x^17 + 64*x^16 + 96*x^15 + 16*x^13 + 96*x^11 + 25*x^9 + 124*x^7 + 112*x^6 + 86*x^5 + 112*x^4 + 124*x^3 + 80*x^2 + 33*x + 80, x^73 + 60*x^71 + 36*x^70 + 62*x^69 + 124*x^68 + 44*x^67 + 28*x^66 + 97*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 100*x^6 + 62*x^5 + 60*x^4 + 108*x^3 + 92*x^2 + 73*x + 4, x^73 + 60*x^71 + 100*x^70 + 62*x^69 + 124*x^68 + 44*x^67 + 92*x^66 + 97*x^65 + 68*x^64 + 96*x^63 + 32*x^62 + 80*x^61 + 96*x^60 + 96*x^59 + 96*x^58 + 52*x^57 + 32*x^56 + 80*x^55 + 48*x^54 + 72*x^53 + 80*x^52 + 16*x^51 + 80*x^50 + 100*x^49 + 48*x^48 + 32*x^47 + 96*x^46 + 48*x^45 + 32*x^44 + 32*x^43 + 32*x^42 + 46*x^41 + 96*x^40 + 40*x^39 + 24*x^38 + 116*x^37 + 40*x^36 + 72*x^35 + 104*x^34 + 30*x^33 + 88*x^32 + 32*x^31 + 96*x^30 + 48*x^29 + 32*x^28 + 32*x^27 + 32*x^26 + 68*x^25 + 96*x^24 + 80*x^23 + 48*x^22 + 72*x^21 + 80*x^20 + 16*x^19 + 80*x^18 + 84*x^17 + 48*x^16 + 96*x^15 + 32*x^14 + 80*x^13 + 96*x^12 + 96*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 124*x^7 + 36*x^6 + 62*x^5 + 60*x^4 + 108*x^3 + 28*x^2 + 73*x + 4, x^73 + 60*x^71 + 124*x^70 + 94*x^69 + 4*x^68 + 44*x^67 + 68*x^66 + 65*x^65 + 60*x^64 + 96*x^63 + 96*x^62 + 80*x^61 + 32*x^60 + 96*x^59 + 32*x^58 + 52*x^57 + 96*x^56 + 80*x^55 + 80*x^54 + 72*x^53 + 48*x^52 + 16*x^51 + 48*x^50 + 100*x^49 + 80*x^48 + 32*x^47 + 32*x^46 + 48*x^45 + 96*x^44 + 32*x^43 + 96*x^42 + 46*x^41 + 32*x^40 + 40*x^39 + 40*x^38 + 52*x^37 + 88*x^36 + 72*x^35 + 88*x^34 + 94*x^33 + 40*x^32 + 32*x^31 + 32*x^30 + 48*x^29 + 96*x^28 + 32*x^27 + 96*x^26 + 68*x^25 + 32*x^24 + 80*x^23 + 80*x^22 + 72*x^21 + 48*x^20 + 16*x^19 + 48*x^18 + 84*x^17 + 80*x^16 + 96*x^15 + 96*x^14 + 80*x^13 + 32*x^12 + 96*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 124*x^7 + 60*x^6 + 94*x^5 + 68*x^4 + 108*x^3 + 4*x^2 + 41*x + 124, x^73 + 60*x^71 + 72*x^70 + 38*x^69 + 40*x^68 + 92*x^67 + 24*x^66 + 73*x^65 + 120*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 100*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 14*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 38*x^5 + 40*x^4 + 28*x^3 + 24*x^2 + 49*x + 120, x^73 + 60*x^71 + 72*x^70 + 86*x^69 + 120*x^68 + 60*x^67 + 120*x^66 + 57*x^65 + 72*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 104*x^53 + 32*x^52 + 80*x^51 + 32*x^50 + 4*x^49 + 96*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 4*x^37 + 80*x^36 + 40*x^35 + 80*x^34 + 46*x^33 + 48*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 104*x^21 + 32*x^20 + 80*x^19 + 32*x^18 + 116*x^17 + 96*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 86*x^5 + 120*x^4 + 124*x^3 + 120*x^2 + 33*x + 72, x^73 + 60*x^71 + 72*x^70 + 6*x^69 + 40*x^68 + 92*x^67 + 88*x^66 + 105*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 96*x^54 + 40*x^53 + 96*x^52 + 80*x^51 + 32*x^50 + 68*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 48*x^38 + 36*x^37 + 112*x^36 + 104*x^35 + 16*x^34 + 78*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 96*x^22 + 40*x^21 + 96*x^20 + 80*x^19 + 32*x^18 + 52*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 72*x^6 + 6*x^5 + 40*x^4 + 28*x^3 + 88*x^2 + 81*x + 56, x^73 + 60*x^71 + 88*x^70 + 22*x^69 + 8*x^68 + 124*x^67 + 104*x^66 + 57*x^65 + 56*x^64 + 96*x^63 + 64*x^62 + 16*x^61 + 64*x^60 + 96*x^59 + 64*x^58 + 116*x^57 + 64*x^56 + 80*x^55 + 32*x^54 + 104*x^53 + 96*x^52 + 80*x^51 + 96*x^50 + 4*x^49 + 32*x^48 + 32*x^47 + 64*x^46 + 112*x^45 + 64*x^44 + 32*x^43 + 64*x^42 + 110*x^41 + 64*x^40 + 40*x^39 + 16*x^38 + 4*x^37 + 48*x^36 + 40*x^35 + 112*x^34 + 46*x^33 + 80*x^32 + 32*x^31 + 64*x^30 + 112*x^29 + 64*x^28 + 32*x^27 + 64*x^26 + 4*x^25 + 64*x^24 + 80*x^23 + 32*x^22 + 104*x^21 + 96*x^20 + 80*x^19 + 96*x^18 + 116*x^17 + 32*x^16 + 96*x^15 + 64*x^14 + 16*x^13 + 64*x^12 + 96*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 124*x^7 + 88*x^6 + 22*x^5 + 8*x^4 + 60*x^3 + 104*x^2 + 33*x + 56}


In [6]:
#check Lemma 5.3
def lem53Polynomials():
	R.<x>=PolynomialRing(QQ)
	ll2=getCoeffsWeaklyType2(7,[1,-107,4896])
	llshift2=[R(list(reversed(l)))(x+1) for l in ll2]
	lllist2=[list(reversed(l.coefficients(sparse=False))) for l in llshift2]
	out=listPowerReduceOddPC(lllist2,(x+5)^56*(x-15)^12,scc757,7)
	return out

def checkLemma53():
	R.<x>=PolynomialRing(QQ)
	print "--- Candidates for char poly corresponding to 75 lines ---"
	print ""
	tic = time.time()
	cand75red=lem53Polynomials()
	toc = time.time()
	print "Time taken to compute char poly candidates: " + str(toc-tic) + " seconds"
	print ""
	print "Candidates for char poly:"
	for i in range(len(cand75red)):
		ff=R(list(reversed(cand75red[i])))*(x+5)^56*(x-15)^12
		ms=R(ff/gcd(ff,ff.derivative()))
		print i+1, factor(ff)
	print ""
	cand75=[cand75red[i] for i in [1,4,2,3,5,6]]
	FarkasCertificates=[
	[18413,257776,0,0,1876556160],
	[9645,135016,0,0,888359172],
	[-1033,-3203, 0, 0, 0], 
	[16674,123379, 523203, 0, 0, 0],
	[5571, 72416, 0, 0, 417044628],
	[-1337,-3999, 0, 0, 0]
	]
	bag=[]
	for i in range(len(cand75)):
		ff=R(list(reversed(cand75[i])))*(x+5)^56*(x-15)^12
		ms=R(ff/gcd(ff,ff.derivative()))
		g=R(ff.derivative()/gcd(ff,ff.derivative()))
		deg=ms.degree()
		f=ms+74*x^(deg-2)
		coeffs=list(reversed(f.coefficients(sparse=False)))
		gf=x^(deg-3)*R([coeffs[2],coeffs[1],coeffs[0]])
		ggf=gf(x-1)
		clist=list(reversed(ggf.coefficients(sparse=False)))
		print "------- Infeasibility of " + str(factor(ff)) + " -------"
		print ""
		tic = time.time()
		ll=getCoeffsType2(deg-1,[clist[0],clist[1],clist[2]])
		llpol=[R(list(reversed(l)))(x+1) for l in ll]
		ll2=[list(reversed(l.coefficients(sparse=False))) for l in llpol]
		bag+=[[factor(ff),listInterlaceReduce(ll2,ms)]]
		toc = time.time()
		print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
		print ""
		deg=ms.degree()
		numrows=len(bag[i][1])
		m=matrix(numrows,deg,[bag[i][1][j] for j in range(numrows)])
		gg=vector(list(reversed(g.coefficients(sparse=False))))
		print "Coefficient matrix A for interlacing char polys:"
		print m
		print ""
		mm=vector(list(reversed(FarkasCertificates[i])))
		print "Certificate of infeasibility c:"
		print "c = " + str(mm)
		ac=mm*m.transpose()
		print "Ac >= 0: " + str(isAtLeastZero(ac))
		print "Ac = " + str(ac)
		innerprod=sum([gg[j]*mm[j] for j in range(deg)])
		print "<g,c> < 0: " + str(innerprod < 0)
		print "<g,c> = " + str(innerprod)
		print ""



# check Lemma 5.4
# (x + 5)^56*(x-13)^4*(x-15)^14*(x-18)
def lem54InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll2=getCoeffsType2(3,[1,-44,628])
	llshift2=[R(list(reversed(l)))(x+1) for l in ll2]
	lllist2=[list(reversed(l.coefficients(sparse=False))) for l in llshift2]
	llred2=listInterlaceReduce(lllist2,(x+5)*(x-13)*(x-15)*(x-18))
	return listPowerReduce(llred2,(x+5)^55*(x-13)^3*(x-15)^13)

def checkLemma54Part1():
	R.<x>=PolynomialRing(QQ)
	tic = time.time()
	llSeidelred=lem54InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	print "Interlacing characteristic polynomials:"
	for i in range(len(llSeidelred)):
		ff=R(list(reversed(llSeidelred[i])))*(x+5)^55*(x-13)^3*(x-15)^13
		ms=R(ff/gcd(ff,ff.derivative()))
		print i+1, factor(ff)
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,4,[llSeidelred[j] for j in range(numrows)])
	mults=vector([56,4,14,1])
	froots=[-5,13,15,18]
	f=prod([(x-r) for r in froots])
	fbas=[R(f/(x-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(4,4,[fbaslist[j] for j in range(4)])
	bb=mults*fbasm
	#submatrix of m without f1
	mf1=m[range(1,numrows),range(4)]
	print "Matrix A' corresponding to interlacing polynomials without f1:" 
	print mf1
	print "" 
	#Farkas certificate 
	fc1=vector(list(reversed([151,0,0,349511])))
	print "Certificate of warranty c:"
	print "c = " + str(fc1)  
	ac = fc1*mf1.transpose()
	print "Ac >= 0: " + str(isAtLeastZero(ac))
	print "Ac = " + str(ac)
	innerprod = sum([fc1[j]*bb[j] for j in range(4)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)

def lem54InterlacingCharacteristicPolynomials2():
	R.<x>=PolynomialRing(QQ)
	ll2=getCoeffsWeaklyType2(5,[1,-69,1880])
	llshift2=[R(list(reversed(l)))(x+1) for l in ll2]
	lllist2=[list(reversed(l.coefficients(sparse=False))) for l in llshift2]
	llred2=listInterlaceReduce(lllist2,(x+5)*(x-13)*(x-15)*(x^3-41*x^2+543*x-2319))
	return listPowerReduceOddPC(llred2,(x+5)^54*(x-13)^2*(x-15)^12,scc737,7)

def checkLemma54Part2():
	R.<x>=PolynomialRing(QQ)
	tic = time.time()
	llSeidelred=lem54InterlacingCharacteristicPolynomials2()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	print "Interlacing characteristic polynomials:"
	for i in range(len(llSeidelred)):
		ff=R(list(reversed(llSeidelred[i])))*(x+5)^54*(x-13)^2*(x-15)^12
		ms=R(ff/gcd(ff,ff.derivative()))
		print i+1, factor(ff)
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,6,[llSeidelred[j] for j in range(numrows)])
	mults=vector([55,3,13,1,1,1])
	N.<al>=NumberField(x^3-41*x^2 + 543*x -2319)
	N1.<z>=PolynomialRing(N)
	N2.<be>=NumberField(z^2 + (al - 41)*z + al^2 - 41*al + 543)
	NN.<zz>=PolynomialRing(N2)
	froots=[-5,13,15,al,be,41-al-be]
	f=prod([(z-r) for r in froots])
	fbas=[NN(f/(z-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(6,6,[fbaslist[j] for j in range(6)])
	bb=mults*fbasm
	print "Coefficient matrix A for interlacing char polys:"
	print m
	print ""
	#Farkas certificate 
	fc1=vector([55783250920,0,0,4439925,330721,24804]) 
	print "Certificate of infeasibility c:"
	print "c = " + str(fc1)  
	ac = fc1*m.transpose()
	print "Ac >= 0: " + str(isAtLeastZero(ac))
	print "Ac = " + str(ac)
	innerprod = sum([fc1[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(RR(innerprod) < 0)
	print "<g,c> = " + str(innerprod)

def checkLemma54():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x + 5)^56*(x-13)^4*(x-15)^14*(x-18))) + "  ---"
	print ""
	checkLemma54Part1()
	print ""
	print "--- Infeasibility of f1 ---"
	print ""
	checkLemma54Part2()

In [7]:
#precompute Seidel char polys classes n=95, e=7
#scc957=SeidelCharPolysMod(95,7)

In [8]:
scc957={x^95 + 15*x^93 + 2*x^92 + 53*x^91 + 4*x^90 + 51*x^89 + 54*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 34*x^84 + 9*x^83 + 28*x^82 + 47*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 115*x^75 + 76*x^74 + 5*x^73 + 10*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 46*x^68 + 119*x^67 + 84*x^66 + 113*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 105*x^27 + 84*x^26 + 31*x^25 + 14*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 106*x^20 + 109*x^19 + 76*x^18 + 43*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 87*x^11 + 28*x^10 + 65*x^9 + 66*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 86*x^4 + 43*x^3 + 4*x^2 + 29*x + 34, x^95 + 15*x^93 + 66*x^92 + 85*x^91 + 68*x^90 + 19*x^89 + 54*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 98*x^84 + 105*x^83 + 92*x^82 + 79*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 83*x^75 + 12*x^74 + 37*x^73 + 10*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 110*x^68 + 23*x^67 + 20*x^66 + 81*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 9*x^27 + 20*x^26 + 127*x^25 + 14*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 42*x^20 + 77*x^19 + 12*x^18 + 75*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 55*x^11 + 92*x^10 + 97*x^9 + 66*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 22*x^4 + 75*x^3 + 68*x^2 + 125*x + 34, x^95 + 15*x^93 + 106*x^92 + 5*x^91 + 52*x^90 + 3*x^89 + 46*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 10*x^84 + 121*x^83 + 108*x^82 + 31*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 99*x^75 + 92*x^74 + 117*x^73 + 18*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 6*x^68 + 71*x^67 + 68*x^66 + 65*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 121*x^27 + 68*x^26 + 47*x^25 + 102*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 114*x^20 + 29*x^19 + 92*x^18 + 91*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 7*x^11 + 108*x^10 + 113*x^9 + 42*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 78*x^4 + 59*x^3 + 52*x^2 + 45*x + 10, x^95 + 15*x^93 + 38*x^92 + 117*x^91 + 28*x^90 + 19*x^89 + 18*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 102*x^84 + 73*x^83 + 4*x^82 + 79*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 51*x^75 + 20*x^74 + 37*x^73 + 110*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 74*x^68 + 55*x^67 + 12*x^66 + 81*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 41*x^27 + 76*x^26 + 127*x^25 + 90*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 62*x^20 + 45*x^19 + 84*x^18 + 75*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 23*x^11 + 68*x^10 + 97*x^9 + 86*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 66*x^4 + 107*x^3 + 92*x^2 + 125*x + 86, x^95 + 15*x^93 + 90*x^92 + 101*x^91 + 52*x^90 + 35*x^89 + 94*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 58*x^84 + 25*x^83 + 108*x^82 + 127*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 3*x^75 + 92*x^74 + 85*x^73 + 98*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 86*x^68 + 39*x^67 + 68*x^66 + 97*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 89*x^27 + 68*x^26 + 79*x^25 + 86*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 98*x^20 + 61*x^19 + 92*x^18 + 59*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 39*x^11 + 108*x^10 + 81*x^9 + 58*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 94*x^4 + 27*x^3 + 52*x^2 + 77*x + 90, x^95 + 15*x^93 + 98*x^92 + 69*x^91 + 52*x^90 + 99*x^89 + 102*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 98*x^84 + 57*x^83 + 44*x^82 + 63*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 35*x^75 + 92*x^74 + 21*x^73 + 26*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 46*x^68 + 7*x^67 + 4*x^66 + 33*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 57*x^27 + 68*x^26 + 15*x^25 + 126*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 42*x^20 + 93*x^19 + 28*x^18 + 123*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 71*x^11 + 108*x^10 + 17*x^9 + 18*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 86*x^4 + 123*x^3 + 116*x^2 + 13*x + 82, x^95 + 15*x^93 + 74*x^92 + 21*x^91 + 100*x^90 + 51*x^89 + 94*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 74*x^84 + 41*x^83 + 124*x^82 + 47*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 19*x^75 + 108*x^74 + 5*x^73 + 34*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 6*x^68 + 87*x^67 + 116*x^66 + 113*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 73*x^27 + 52*x^26 + 31*x^25 + 86*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 50*x^20 + 13*x^19 + 44*x^18 + 43*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 119*x^11 + 60*x^10 + 65*x^9 + 122*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 78*x^4 + 11*x^3 + 36*x^2 + 29*x + 58, x^95 + 15*x^93 + 122*x^92 + 37*x^91 + 20*x^90 + 35*x^89 + 94*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 26*x^84 + 89*x^83 + 12*x^82 + 127*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 67*x^75 + 124*x^74 + 85*x^73 + 98*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 118*x^68 + 103*x^67 + 36*x^66 + 97*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 25*x^27 + 36*x^26 + 79*x^25 + 86*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 66*x^20 + 125*x^19 + 124*x^18 + 59*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 103*x^11 + 12*x^10 + 81*x^9 + 58*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 126*x^4 + 91*x^3 + 20*x^2 + 77*x + 26, x^95 + 15*x^93 + 86*x^92 + 37*x^91 + 12*x^90 + 99*x^89 + 82*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 54*x^84 + 89*x^83 + 84*x^82 + 63*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 67*x^75 + 100*x^74 + 21*x^73 + 110*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 58*x^68 + 103*x^67 + 124*x^66 + 33*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 25*x^27 + 124*x^26 + 15*x^25 + 26*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 78*x^20 + 125*x^19 + 100*x^18 + 123*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 103*x^11 + 84*x^10 + 17*x^9 + 86*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 114*x^4 + 91*x^3 + 12*x^2 + 13*x + 118, x^95 + 15*x^93 + 6*x^92 + 101*x^91 + 108*x^90 + 35*x^89 + 98*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 102*x^84 + 25*x^83 + 116*x^82 + 127*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 3*x^75 + 4*x^74 + 85*x^73 + 94*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 10*x^68 + 39*x^67 + 92*x^66 + 97*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 89*x^27 + 92*x^26 + 79*x^25 + 106*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 62*x^20 + 61*x^19 + 4*x^18 + 59*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 39*x^11 + 116*x^10 + 81*x^9 + 6*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 2*x^4 + 27*x^3 + 108*x^2 + 77*x + 38, x^95 + 15*x^93 + 10*x^92 + 85*x^91 + 68*x^90 + 115*x^89 + 62*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 74*x^84 + 105*x^83 + 28*x^82 + 111*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 83*x^75 + 12*x^74 + 69*x^73 + 66*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 6*x^68 + 23*x^67 + 84*x^66 + 49*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 9*x^27 + 20*x^26 + 95*x^25 + 54*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 50*x^20 + 77*x^19 + 76*x^18 + 107*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 55*x^11 + 92*x^10 + x^9 + 26*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 78*x^4 + 75*x^3 + 4*x^2 + 93*x + 26, x^95 + 15*x^93 + 38*x^92 + 5*x^91 + 76*x^90 + 3*x^89 + 34*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 70*x^84 + 121*x^83 + 20*x^82 + 31*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 99*x^75 + 36*x^74 + 117*x^73 + 30*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 42*x^68 + 71*x^67 + 60*x^66 + 65*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 121*x^27 + 60*x^26 + 47*x^25 + 42*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 30*x^20 + 29*x^19 + 36*x^18 + 91*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 7*x^11 + 20*x^10 + 113*x^9 + 70*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 34*x^4 + 59*x^3 + 76*x^2 + 45*x + 38, x^95 + 15*x^93 + 34*x^92 + 37*x^91 + 20*x^90 + 3*x^89 + 70*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 98*x^84 + 89*x^83 + 76*x^82 + 31*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 67*x^75 + 124*x^74 + 117*x^73 + 58*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 46*x^68 + 103*x^67 + 100*x^66 + 65*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 25*x^27 + 36*x^26 + 47*x^25 + 94*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 42*x^20 + 125*x^19 + 60*x^18 + 91*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 103*x^11 + 12*x^10 + 113*x^9 + 50*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 86*x^4 + 91*x^3 + 84*x^2 + 45*x + 50, x^95 + 15*x^93 + 122*x^92 + 69*x^91 + 84*x^90 + 67*x^89 + 94*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 26*x^84 + 57*x^83 + 76*x^82 + 95*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 35*x^75 + 60*x^74 + 53*x^73 + 98*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 118*x^68 + 7*x^67 + 100*x^66 + x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 57*x^27 + 100*x^26 + 111*x^25 + 86*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 66*x^20 + 93*x^19 + 60*x^18 + 27*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 71*x^11 + 76*x^10 + 49*x^9 + 58*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 126*x^4 + 123*x^3 + 84*x^2 + 109*x + 26, x^95 + 15*x^93 + 106*x^92 + 69*x^91 + 20*x^90 + 3*x^89 + 14*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 74*x^84 + 57*x^83 + 12*x^82 + 31*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 35*x^75 + 124*x^74 + 117*x^73 + 50*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 70*x^68 + 7*x^67 + 36*x^66 + 65*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 57*x^27 + 36*x^26 + 47*x^25 + 70*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 50*x^20 + 93*x^19 + 124*x^18 + 91*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 71*x^11 + 12*x^10 + 113*x^9 + 74*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 14*x^4 + 123*x^3 + 20*x^2 + 45*x + 106, x^95 + 15*x^93 + 54*x^92 + 37*x^91 + 44*x^90 + 35*x^89 + 82*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 86*x^84 + 89*x^83 + 52*x^82 + 127*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 67*x^75 + 68*x^74 + 85*x^73 + 110*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 26*x^68 + 103*x^67 + 28*x^66 + 97*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 25*x^27 + 28*x^26 + 79*x^25 + 26*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 110*x^20 + 125*x^19 + 68*x^18 + 59*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 103*x^11 + 52*x^10 + 81*x^9 + 86*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 82*x^4 + 91*x^3 + 44*x^2 + 77*x + 54, x^95 + 15*x^93 + 122*x^92 + 21*x^91 + 4*x^90 + 51*x^89 + 46*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 122*x^84 + 41*x^83 + 92*x^82 + 47*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 19*x^75 + 76*x^74 + 5*x^73 + 82*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 86*x^68 + 87*x^67 + 20*x^66 + 113*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 73*x^27 + 84*x^26 + 31*x^25 + 102*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 34*x^20 + 13*x^19 + 12*x^18 + 43*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 119*x^11 + 28*x^10 + 65*x^9 + 106*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 94*x^4 + 11*x^3 + 68*x^2 + 29*x + 42, x^95 + 15*x^93 + 110*x^92 + 69*x^91 + 44*x^90 + 99*x^89 + 74*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 110*x^84 + 57*x^83 + 116*x^82 + 63*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 35*x^75 + 68*x^74 + 21*x^73 + 54*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 2*x^68 + 7*x^67 + 92*x^66 + 33*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 57*x^27 + 28*x^26 + 15*x^25 + 114*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 102*x^20 + 93*x^19 + 4*x^18 + 123*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 71*x^11 + 52*x^10 + 17*x^9 + 126*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 26*x^4 + 123*x^3 + 108*x^2 + 13*x + 62, x^95 + 15*x^93 + 74*x^92 + 117*x^91 + 36*x^90 + 83*x^89 + 30*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 74*x^84 + 73*x^83 + 60*x^82 + 15*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 51*x^75 + 44*x^74 + 101*x^73 + 98*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 6*x^68 + 55*x^67 + 52*x^66 + 17*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 41*x^27 + 116*x^26 + 63*x^25 + 22*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 50*x^20 + 45*x^19 + 108*x^18 + 11*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 23*x^11 + 124*x^10 + 33*x^9 + 58*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 78*x^4 + 107*x^3 + 100*x^2 + 61*x + 122, x^95 + 15*x^93 + 78*x^92 + 85*x^91 + 124*x^90 + 83*x^89 + 26*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 110*x^84 + 105*x^83 + 100*x^82 + 15*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 83*x^75 + 52*x^74 + 101*x^73 + 38*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 66*x^68 + 23*x^67 + 44*x^66 + 17*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 9*x^27 + 44*x^26 + 63*x^25 + 2*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 102*x^20 + 77*x^19 + 52*x^18 + 11*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 55*x^11 + 100*x^10 + 33*x^9 + 46*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 90*x^4 + 75*x^3 + 124*x^2 + 61*x + 14, x^95 + 15*x^93 + 86*x^92 + 53*x^91 + 28*x^90 + 19*x^89 + 66*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 86*x^84 + 9*x^83 + 4*x^82 + 79*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 115*x^75 + 20*x^74 + 37*x^73 + 62*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 90*x^68 + 119*x^67 + 12*x^66 + 81*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 105*x^27 + 76*x^26 + 127*x^25 + 74*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 110*x^20 + 109*x^19 + 84*x^18 + 75*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 87*x^11 + 68*x^10 + 97*x^9 + 102*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 18*x^4 + 43*x^3 + 92*x^2 + 125*x + 38, x^95 + 15*x^93 + 6*x^92 + 5*x^91 + 108*x^90 + 67*x^89 + 34*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 102*x^84 + 121*x^83 + 116*x^82 + 95*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 99*x^75 + 4*x^74 + 53*x^73 + 30*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 10*x^68 + 71*x^67 + 92*x^66 + x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 121*x^27 + 92*x^26 + 111*x^25 + 42*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 62*x^20 + 29*x^19 + 4*x^18 + 27*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 7*x^11 + 116*x^10 + 49*x^9 + 70*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 2*x^4 + 59*x^3 + 108*x^2 + 109*x + 102, x^95 + 15*x^93 + 50*x^92 + 69*x^91 + 84*x^90 + 35*x^89 + 22*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 50*x^84 + 57*x^83 + 12*x^82 + 127*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 35*x^75 + 60*x^74 + 85*x^73 + 106*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 94*x^68 + 7*x^67 + 36*x^66 + 97*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 57*x^27 + 100*x^26 + 79*x^25 + 110*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 58*x^20 + 93*x^19 + 124*x^18 + 59*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 71*x^11 + 76*x^10 + 81*x^9 + 34*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 70*x^4 + 123*x^3 + 20*x^2 + 77*x + 98, x^95 + 15*x^93 + 70*x^92 + 69*x^91 + 12*x^90 + 67*x^89 + 2*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 102*x^84 + 57*x^83 + 84*x^82 + 95*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 35*x^75 + 100*x^74 + 53*x^73 + 62*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 10*x^68 + 7*x^67 + 124*x^66 + x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 57*x^27 + 124*x^26 + 111*x^25 + 10*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 62*x^20 + 93*x^19 + 100*x^18 + 27*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 71*x^11 + 84*x^10 + 49*x^9 + 102*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 2*x^4 + 123*x^3 + 12*x^2 + 109*x + 70, x^95 + 15*x^93 + 106*x^92 + 5*x^91 + 52*x^90 + 67*x^89 + 110*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 10*x^84 + 121*x^83 + 108*x^82 + 95*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 99*x^75 + 92*x^74 + 53*x^73 + 82*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 6*x^68 + 71*x^67 + 68*x^66 + x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 121*x^27 + 68*x^26 + 111*x^25 + 38*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 114*x^20 + 29*x^19 + 92*x^18 + 27*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 7*x^11 + 108*x^10 + 49*x^9 + 106*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 78*x^4 + 59*x^3 + 52*x^2 + 109*x + 74, x^95 + 15*x^93 + 58*x^92 + 69*x^91 + 20*x^90 + 3*x^89 + 30*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 90*x^84 + 57*x^83 + 12*x^82 + 31*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 35*x^75 + 124*x^74 + 117*x^73 + 34*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 54*x^68 + 7*x^67 + 36*x^66 + 65*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 57*x^27 + 36*x^26 + 47*x^25 + 22*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 2*x^20 + 93*x^19 + 124*x^18 + 91*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 71*x^11 + 12*x^10 + 113*x^9 + 122*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 62*x^4 + 123*x^3 + 20*x^2 + 45*x + 90, x^95 + 15*x^93 + 106*x^92 + 117*x^91 + 100*x^90 + 19*x^89 + 62*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 106*x^84 + 73*x^83 + 124*x^82 + 79*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 51*x^75 + 108*x^74 + 37*x^73 + 66*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 102*x^68 + 55*x^67 + 116*x^66 + 81*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 41*x^27 + 52*x^26 + 127*x^25 + 54*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 82*x^20 + 45*x^19 + 44*x^18 + 75*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 23*x^11 + 60*x^10 + 97*x^9 + 26*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 46*x^4 + 107*x^3 + 36*x^2 + 125*x + 90, x^95 + 15*x^93 + 98*x^92 + 69*x^91 + 52*x^90 + 35*x^89 + 38*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 98*x^84 + 57*x^83 + 44*x^82 + 127*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 35*x^75 + 92*x^74 + 85*x^73 + 90*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 46*x^68 + 7*x^67 + 4*x^66 + 97*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 57*x^27 + 68*x^26 + 79*x^25 + 62*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 42*x^20 + 93*x^19 + 28*x^18 + 59*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 71*x^11 + 108*x^10 + 81*x^9 + 82*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 86*x^4 + 123*x^3 + 116*x^2 + 77*x + 18, x^95 + 15*x^93 + 46*x^92 + 37*x^91 + 108*x^90 + 3*x^89 + 74*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 46*x^84 + 89*x^83 + 52*x^82 + 31*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 67*x^75 + 4*x^74 + 117*x^73 + 54*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 66*x^68 + 103*x^67 + 28*x^66 + 65*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 25*x^27 + 92*x^26 + 47*x^25 + 114*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 38*x^20 + 125*x^19 + 68*x^18 + 91*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 103*x^11 + 116*x^10 + 113*x^9 + 126*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 90*x^4 + 91*x^3 + 44*x^2 + 45*x + 62, x^95 + 15*x^93 + 46*x^92 + 117*x^91 + 60*x^90 + 115*x^89 + 122*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 78*x^84 + 73*x^83 + 36*x^82 + 111*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 51*x^75 + 116*x^74 + 69*x^73 + 70*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 98*x^68 + 55*x^67 + 108*x^66 + 49*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 41*x^27 + 108*x^26 + 95*x^25 + 98*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 70*x^20 + 45*x^19 + 116*x^18 + 107*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 23*x^11 + 36*x^10 + x^9 + 78*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 122*x^4 + 107*x^3 + 60*x^2 + 93*x + 46, x^95 + 15*x^93 + 86*x^92 + 53*x^91 + 28*x^90 + 83*x^89 + 2*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 86*x^84 + 9*x^83 + 4*x^82 + 15*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 115*x^75 + 20*x^74 + 101*x^73 + 126*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 90*x^68 + 119*x^67 + 12*x^66 + 17*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 105*x^27 + 76*x^26 + 63*x^25 + 10*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 110*x^20 + 109*x^19 + 84*x^18 + 11*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 87*x^11 + 68*x^10 + 33*x^9 + 38*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 18*x^4 + 43*x^3 + 92*x^2 + 61*x + 102, x^95 + 15*x^93 + 26*x^92 + 5*x^91 + 116*x^90 + 67*x^89 + 30*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 122*x^84 + 121*x^83 + 44*x^82 + 95*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 99*x^75 + 28*x^74 + 53*x^73 + 34*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 22*x^68 + 71*x^67 + 4*x^66 + x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 121*x^27 + 4*x^26 + 111*x^25 + 22*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 34*x^20 + 29*x^19 + 28*x^18 + 27*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 7*x^11 + 44*x^10 + 49*x^9 + 122*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 30*x^4 + 59*x^3 + 116*x^2 + 109*x + 26, x^95 + 15*x^93 + 22*x^92 + 69*x^91 + 108*x^90 + 3*x^89 + 114*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 54*x^84 + 57*x^83 + 116*x^82 + 31*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 35*x^75 + 4*x^74 + 117*x^73 + 78*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 58*x^68 + 7*x^67 + 92*x^66 + 65*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 57*x^27 + 92*x^26 + 47*x^25 + 58*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 78*x^20 + 93*x^19 + 4*x^18 + 91*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 71*x^11 + 116*x^10 + 113*x^9 + 54*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 114*x^4 + 123*x^3 + 108*x^2 + 45*x + 22, x^95 + 15*x^93 + 6*x^92 + 5*x^91 + 44*x^90 + 67*x^89 + 98*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 102*x^84 + 121*x^83 + 52*x^82 + 95*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 99*x^75 + 68*x^74 + 53*x^73 + 94*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 10*x^68 + 71*x^67 + 28*x^66 + x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 121*x^27 + 28*x^26 + 111*x^25 + 106*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 62*x^20 + 29*x^19 + 68*x^18 + 27*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 7*x^11 + 52*x^10 + 49*x^9 + 6*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 2*x^4 + 59*x^3 + 44*x^2 + 109*x + 38, x^95 + 15*x^93 + 86*x^92 + 69*x^91 + 44*x^90 + 3*x^89 + 114*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 118*x^84 + 57*x^83 + 52*x^82 + 31*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 35*x^75 + 68*x^74 + 117*x^73 + 78*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 122*x^68 + 7*x^67 + 28*x^66 + 65*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 57*x^27 + 28*x^26 + 47*x^25 + 58*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 14*x^20 + 93*x^19 + 68*x^18 + 91*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 71*x^11 + 52*x^10 + 113*x^9 + 54*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 50*x^4 + 123*x^3 + 44*x^2 + 45*x + 22, x^95 + 15*x^93 + 106*x^92 + 37*x^91 + 20*x^90 + 35*x^89 + 14*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 74*x^84 + 89*x^83 + 12*x^82 + 127*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 67*x^75 + 124*x^74 + 85*x^73 + 50*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 70*x^68 + 103*x^67 + 36*x^66 + 97*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 25*x^27 + 36*x^26 + 79*x^25 + 70*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 50*x^20 + 125*x^19 + 124*x^18 + 59*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 103*x^11 + 12*x^10 + 81*x^9 + 74*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 14*x^4 + 91*x^3 + 20*x^2 + 77*x + 106, x^95 + 15*x^93 + 110*x^92 + 117*x^91 + 28*x^90 + 115*x^89 + 90*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 78*x^84 + 73*x^83 + 68*x^82 + 111*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 51*x^75 + 20*x^74 + 69*x^73 + 102*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 98*x^68 + 55*x^67 + 76*x^66 + 49*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 41*x^27 + 76*x^26 + 95*x^25 + 66*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 70*x^20 + 45*x^19 + 20*x^18 + 107*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 23*x^11 + 68*x^10 + x^9 + 110*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 122*x^4 + 107*x^3 + 28*x^2 + 93*x + 14, x^95 + 15*x^93 + 6*x^92 + 53*x^91 + 124*x^90 + 19*x^89 + 82*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 6*x^84 + 9*x^83 + 36*x^82 + 79*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 115*x^75 + 52*x^74 + 37*x^73 + 46*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 42*x^68 + 119*x^67 + 108*x^66 + 81*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 105*x^27 + 44*x^26 + 127*x^25 + 26*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 94*x^20 + 109*x^19 + 116*x^18 + 75*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 87*x^11 + 100*x^10 + 97*x^9 + 22*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 34*x^4 + 43*x^3 + 60*x^2 + 125*x + 86, x^95 + 15*x^93 + 126*x^92 + 37*x^91 + 108*x^90 + 3*x^89 + 90*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 62*x^84 + 89*x^83 + 52*x^82 + 31*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 67*x^75 + 4*x^74 + 117*x^73 + 38*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 50*x^68 + 103*x^67 + 28*x^66 + 65*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 25*x^27 + 92*x^26 + 47*x^25 + 66*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 118*x^20 + 125*x^19 + 68*x^18 + 91*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 103*x^11 + 116*x^10 + 113*x^9 + 46*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 10*x^4 + 91*x^3 + 44*x^2 + 45*x + 46, x^95 + 15*x^93 + 90*x^92 + 69*x^91 + 84*x^90 + 67*x^89 + 62*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 122*x^84 + 57*x^83 + 76*x^82 + 95*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 35*x^75 + 60*x^74 + 53*x^73 + 2*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 22*x^68 + 7*x^67 + 100*x^66 + x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 57*x^27 + 100*x^26 + 111*x^25 + 54*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 34*x^20 + 93*x^19 + 60*x^18 + 27*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 71*x^11 + 76*x^10 + 49*x^9 + 90*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 30*x^4 + 123*x^3 + 84*x^2 + 109*x + 58, x^95 + 15*x^93 + 54*x^92 + 21*x^91 + 28*x^90 + 51*x^89 + 34*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 54*x^84 + 41*x^83 + 4*x^82 + 47*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 19*x^75 + 20*x^74 + 5*x^73 + 94*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 122*x^68 + 87*x^67 + 12*x^66 + 113*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 73*x^27 + 76*x^26 + 31*x^25 + 42*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 78*x^20 + 13*x^19 + 84*x^18 + 43*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 119*x^11 + 68*x^10 + 65*x^9 + 6*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 50*x^4 + 11*x^3 + 92*x^2 + 29*x + 70, x^95 + 15*x^93 + 118*x^92 + 117*x^91 + 124*x^90 + 19*x^89 + 66*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 54*x^84 + 73*x^83 + 36*x^82 + 79*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 51*x^75 + 52*x^74 + 37*x^73 + 62*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 122*x^68 + 55*x^67 + 108*x^66 + 81*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 41*x^27 + 44*x^26 + 127*x^25 + 74*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 78*x^20 + 45*x^19 + 116*x^18 + 75*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 23*x^11 + 100*x^10 + 97*x^9 + 102*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 50*x^4 + 107*x^3 + 60*x^2 + 125*x + 102, x^95 + 15*x^93 + 50*x^92 + 101*x^91 + 52*x^90 + 3*x^89 + 54*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 114*x^84 + 25*x^83 + 44*x^82 + 31*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 3*x^75 + 92*x^74 + 117*x^73 + 74*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 30*x^68 + 39*x^67 + 4*x^66 + 65*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 89*x^27 + 68*x^26 + 47*x^25 + 14*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 122*x^20 + 61*x^19 + 28*x^18 + 91*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 39*x^11 + 108*x^10 + 113*x^9 + 2*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 6*x^4 + 27*x^3 + 116*x^2 + 45*x + 2, x^95 + 15*x^93 + 34*x^92 + 5*x^91 + 84*x^90 + 35*x^89 + 6*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 98*x^84 + 121*x^83 + 12*x^82 + 127*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 99*x^75 + 60*x^74 + 85*x^73 + 122*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 46*x^68 + 71*x^67 + 36*x^66 + 97*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 121*x^27 + 100*x^26 + 79*x^25 + 30*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 42*x^20 + 29*x^19 + 124*x^18 + 59*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 7*x^11 + 76*x^10 + 81*x^9 + 114*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 86*x^4 + 59*x^3 + 20*x^2 + 77*x + 114, x^95 + 15*x^93 + 122*x^92 + 21*x^91 + 4*x^90 + 115*x^89 + 110*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 122*x^84 + 41*x^83 + 92*x^82 + 111*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 19*x^75 + 76*x^74 + 69*x^73 + 18*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 86*x^68 + 87*x^67 + 20*x^66 + 49*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 73*x^27 + 84*x^26 + 95*x^25 + 38*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 34*x^20 + 13*x^19 + 12*x^18 + 107*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 119*x^11 + 28*x^10 + x^9 + 42*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 94*x^4 + 11*x^3 + 68*x^2 + 93*x + 106, x^95 + 15*x^93 + 82*x^92 + 21*x^91 + 36*x^90 + 83*x^89 + 38*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 114*x^84 + 41*x^83 + 124*x^82 + 15*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 19*x^75 + 44*x^74 + 101*x^73 + 26*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 94*x^68 + 87*x^67 + 116*x^66 + 17*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 73*x^27 + 116*x^26 + 63*x^25 + 62*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 122*x^20 + 13*x^19 + 44*x^18 + 11*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 119*x^11 + 124*x^10 + 33*x^9 + 18*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 70*x^4 + 11*x^3 + 36*x^2 + 61*x + 114, x^95 + 15*x^93 + 62*x^92 + 85*x^91 + 92*x^90 + 83*x^89 + 106*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 94*x^84 + 105*x^83 + 4*x^82 + 15*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 83*x^75 + 84*x^74 + 101*x^73 + 86*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 82*x^68 + 23*x^67 + 12*x^66 + 17*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 9*x^27 + 12*x^26 + 63*x^25 + 18*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 22*x^20 + 77*x^19 + 84*x^18 + 11*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 55*x^11 + 4*x^10 + 33*x^9 + 30*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 42*x^4 + 75*x^3 + 92*x^2 + 61*x + 126, x^95 + 15*x^93 + 46*x^92 + 53*x^91 + 60*x^90 + 51*x^89 + 122*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 78*x^84 + 9*x^83 + 36*x^82 + 47*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 115*x^75 + 116*x^74 + 5*x^73 + 70*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 98*x^68 + 119*x^67 + 108*x^66 + 113*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 105*x^27 + 108*x^26 + 31*x^25 + 98*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 70*x^20 + 109*x^19 + 116*x^18 + 43*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 87*x^11 + 36*x^10 + 65*x^9 + 78*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 122*x^4 + 43*x^3 + 60*x^2 + 29*x + 46, x^95 + 15*x^93 + 70*x^92 + 117*x^91 + 28*x^90 + 83*x^89 + 114*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 6*x^84 + 73*x^83 + 4*x^82 + 15*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 51*x^75 + 20*x^74 + 101*x^73 + 14*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 42*x^68 + 55*x^67 + 12*x^66 + 17*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 41*x^27 + 76*x^26 + 63*x^25 + 58*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 94*x^20 + 45*x^19 + 84*x^18 + 11*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 23*x^11 + 68*x^10 + 33*x^9 + 118*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 34*x^4 + 107*x^3 + 92*x^2 + 61*x + 118, x^95 + 15*x^93 + 74*x^92 + 117*x^91 + 100*x^90 + 19*x^89 + 30*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 74*x^84 + 73*x^83 + 124*x^82 + 79*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 51*x^75 + 108*x^74 + 37*x^73 + 98*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 6*x^68 + 55*x^67 + 116*x^66 + 81*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 41*x^27 + 52*x^26 + 127*x^25 + 22*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 50*x^20 + 45*x^19 + 44*x^18 + 75*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 23*x^11 + 60*x^10 + 97*x^9 + 58*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 78*x^4 + 107*x^3 + 36*x^2 + 125*x + 122, x^95 + 15*x^93 + 66*x^92 + 21*x^91 + 100*x^90 + 83*x^89 + 22*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 34*x^84 + 41*x^83 + 60*x^82 + 15*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 19*x^75 + 108*x^74 + 101*x^73 + 42*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 46*x^68 + 87*x^67 + 52*x^66 + 17*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 73*x^27 + 52*x^26 + 63*x^25 + 110*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 106*x^20 + 13*x^19 + 108*x^18 + 11*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 119*x^11 + 60*x^10 + 33*x^9 + 98*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 86*x^4 + 11*x^3 + 100*x^2 + 61*x + 2, x^95 + 15*x^93 + 82*x^92 + 117*x^91 + 68*x^90 + 51*x^89 + 70*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 50*x^84 + 73*x^83 + 92*x^82 + 47*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 51*x^75 + 12*x^74 + 5*x^73 + 122*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 30*x^68 + 55*x^67 + 20*x^66 + 113*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 41*x^27 + 20*x^26 + 31*x^25 + 94*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 58*x^20 + 45*x^19 + 12*x^18 + 43*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 23*x^11 + 92*x^10 + 65*x^9 + 114*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 6*x^4 + 107*x^3 + 68*x^2 + 29*x + 18, x^95 + 15*x^93 + 106*x^92 + 69*x^91 + 84*x^90 + 67*x^89 + 14*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 74*x^84 + 57*x^83 + 76*x^82 + 95*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 35*x^75 + 60*x^74 + 53*x^73 + 50*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 70*x^68 + 7*x^67 + 100*x^66 + x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 57*x^27 + 100*x^26 + 111*x^25 + 70*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 50*x^20 + 93*x^19 + 60*x^18 + 27*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 71*x^11 + 76*x^10 + 49*x^9 + 74*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 14*x^4 + 123*x^3 + 84*x^2 + 109*x + 106, x^95 + 15*x^93 + 34*x^92 + 69*x^91 + 20*x^90 + 35*x^89 + 6*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 98*x^84 + 57*x^83 + 76*x^82 + 127*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 35*x^75 + 124*x^74 + 85*x^73 + 122*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 46*x^68 + 7*x^67 + 100*x^66 + 97*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 57*x^27 + 36*x^26 + 79*x^25 + 30*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 42*x^20 + 93*x^19 + 60*x^18 + 59*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 71*x^11 + 12*x^10 + 81*x^9 + 114*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 86*x^4 + 123*x^3 + 84*x^2 + 77*x + 114, x^95 + 15*x^93 + 30*x^92 + 101*x^91 + 108*x^90 + 67*x^89 + 122*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 94*x^84 + 25*x^83 + 52*x^82 + 95*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 3*x^75 + 4*x^74 + 53*x^73 + 6*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 18*x^68 + 39*x^67 + 28*x^66 + x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 89*x^27 + 92*x^26 + 111*x^25 + 98*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 22*x^20 + 61*x^19 + 68*x^18 + 27*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 39*x^11 + 116*x^10 + 49*x^9 + 14*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 106*x^4 + 27*x^3 + 44*x^2 + 109*x + 14, x^95 + 15*x^93 + 42*x^92 + 117*x^91 + 36*x^90 + 19*x^89 + 62*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 42*x^84 + 73*x^83 + 60*x^82 + 79*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 51*x^75 + 44*x^74 + 37*x^73 + 66*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 38*x^68 + 55*x^67 + 52*x^66 + 81*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 41*x^27 + 116*x^26 + 127*x^25 + 54*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 18*x^20 + 45*x^19 + 108*x^18 + 75*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 23*x^11 + 124*x^10 + 97*x^9 + 26*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 110*x^4 + 107*x^3 + 100*x^2 + 125*x + 90, x^95 + 15*x^93 + 114*x^92 + 69*x^91 + 116*x^90 + 99*x^89 + 118*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 50*x^84 + 57*x^83 + 108*x^82 + 63*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 35*x^75 + 28*x^74 + 21*x^73 + 10*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 94*x^68 + 7*x^67 + 68*x^66 + 33*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 57*x^27 + 4*x^26 + 15*x^25 + 78*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 58*x^20 + 93*x^19 + 92*x^18 + 123*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 71*x^11 + 44*x^10 + 17*x^9 + 66*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 70*x^4 + 123*x^3 + 52*x^2 + 13*x + 66, x^95 + 15*x^93 + 114*x^92 + 5*x^91 + 84*x^90 + 35*x^89 + 22*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 114*x^84 + 121*x^83 + 12*x^82 + 127*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 99*x^75 + 60*x^74 + 85*x^73 + 106*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 30*x^68 + 71*x^67 + 36*x^66 + 97*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 121*x^27 + 100*x^26 + 79*x^25 + 110*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 122*x^20 + 29*x^19 + 124*x^18 + 59*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 7*x^11 + 76*x^10 + 81*x^9 + 34*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 6*x^4 + 59*x^3 + 20*x^2 + 77*x + 98, x^95 + 15*x^93 + 22*x^92 + 37*x^91 + 44*x^90 + 99*x^89 + 114*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 54*x^84 + 89*x^83 + 52*x^82 + 63*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 67*x^75 + 68*x^74 + 21*x^73 + 78*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 58*x^68 + 103*x^67 + 28*x^66 + 33*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 25*x^27 + 28*x^26 + 15*x^25 + 58*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 78*x^20 + 125*x^19 + 68*x^18 + 123*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 103*x^11 + 52*x^10 + 17*x^9 + 54*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 114*x^4 + 91*x^3 + 44*x^2 + 13*x + 22, x^95 + 15*x^93 + 10*x^92 + 85*x^91 + 4*x^90 + 51*x^89 + 62*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 74*x^84 + 105*x^83 + 92*x^82 + 47*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 83*x^75 + 76*x^74 + 5*x^73 + 66*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 6*x^68 + 23*x^67 + 20*x^66 + 113*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 9*x^27 + 84*x^26 + 31*x^25 + 54*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 50*x^20 + 77*x^19 + 12*x^18 + 43*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 55*x^11 + 28*x^10 + 65*x^9 + 26*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 78*x^4 + 75*x^3 + 68*x^2 + 29*x + 26, x^95 + 15*x^93 + 110*x^92 + 5*x^91 + 108*x^90 + 99*x^89 + 74*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 110*x^84 + 121*x^83 + 52*x^82 + 63*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 99*x^75 + 4*x^74 + 21*x^73 + 54*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 2*x^68 + 71*x^67 + 28*x^66 + 33*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 121*x^27 + 92*x^26 + 15*x^25 + 114*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 102*x^20 + 29*x^19 + 68*x^18 + 123*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 7*x^11 + 116*x^10 + 17*x^9 + 126*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 26*x^4 + 59*x^3 + 44*x^2 + 13*x + 62, x^95 + 15*x^93 + 106*x^92 + 69*x^91 + 52*x^90 + 3*x^89 + 110*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 10*x^84 + 57*x^83 + 108*x^82 + 31*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 35*x^75 + 92*x^74 + 117*x^73 + 82*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 6*x^68 + 7*x^67 + 68*x^66 + 65*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 57*x^27 + 68*x^26 + 47*x^25 + 38*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 114*x^20 + 93*x^19 + 92*x^18 + 91*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 71*x^11 + 108*x^10 + 113*x^9 + 106*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 78*x^4 + 123*x^3 + 52*x^2 + 45*x + 74, x^95 + 15*x^93 + 38*x^92 + 117*x^91 + 124*x^90 + 19*x^89 + 50*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 38*x^84 + 73*x^83 + 36*x^82 + 79*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 51*x^75 + 52*x^74 + 37*x^73 + 78*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 10*x^68 + 55*x^67 + 108*x^66 + 81*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 41*x^27 + 44*x^26 + 127*x^25 + 122*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 126*x^20 + 45*x^19 + 116*x^18 + 75*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 23*x^11 + 100*x^10 + 97*x^9 + 54*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 2*x^4 + 107*x^3 + 60*x^2 + 125*x + 118, x^95 + 15*x^93 + 122*x^92 + 37*x^91 + 116*x^90 + 99*x^89 + 62*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 90*x^84 + 89*x^83 + 44*x^82 + 63*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 67*x^75 + 28*x^74 + 21*x^73 + 2*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 54*x^68 + 103*x^67 + 4*x^66 + 33*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 25*x^27 + 4*x^26 + 15*x^25 + 54*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 2*x^20 + 125*x^19 + 28*x^18 + 123*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 103*x^11 + 44*x^10 + 17*x^9 + 90*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 62*x^4 + 91*x^3 + 116*x^2 + 13*x + 122, x^95 + 15*x^93 + 30*x^92 + 37*x^91 + 12*x^90 + 3*x^89 + 90*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 30*x^84 + 89*x^83 + 20*x^82 + 31*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 67*x^75 + 100*x^74 + 117*x^73 + 38*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 82*x^68 + 103*x^67 + 60*x^66 + 65*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 25*x^27 + 124*x^26 + 47*x^25 + 66*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 86*x^20 + 125*x^19 + 36*x^18 + 91*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 103*x^11 + 84*x^10 + 113*x^9 + 46*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 42*x^4 + 91*x^3 + 76*x^2 + 45*x + 110, x^95 + 15*x^93 + 58*x^92 + 101*x^91 + 84*x^90 + 35*x^89 + 30*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 90*x^84 + 25*x^83 + 76*x^82 + 127*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 3*x^75 + 60*x^74 + 85*x^73 + 34*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 54*x^68 + 39*x^67 + 100*x^66 + 97*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 89*x^27 + 100*x^26 + 79*x^25 + 22*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 2*x^20 + 61*x^19 + 60*x^18 + 59*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 39*x^11 + 76*x^10 + 81*x^9 + 122*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 62*x^4 + 27*x^3 + 84*x^2 + 77*x + 90, x^95 + 15*x^93 + 58*x^92 + 21*x^91 + 36*x^90 + 115*x^89 + 14*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 122*x^84 + 41*x^83 + 60*x^82 + 111*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 19*x^75 + 44*x^74 + 69*x^73 + 114*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 86*x^68 + 87*x^67 + 52*x^66 + 49*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 73*x^27 + 116*x^26 + 95*x^25 + 70*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 34*x^20 + 13*x^19 + 108*x^18 + 107*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 119*x^11 + 124*x^10 + x^9 + 10*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 94*x^4 + 11*x^3 + 100*x^2 + 93*x + 10, x^95 + 15*x^93 + 102*x^92 + 5*x^91 + 76*x^90 + 67*x^89 + 34*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 6*x^84 + 121*x^83 + 20*x^82 + 95*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 99*x^75 + 36*x^74 + 53*x^73 + 30*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 106*x^68 + 71*x^67 + 60*x^66 + x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 121*x^27 + 60*x^26 + 111*x^25 + 42*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 94*x^20 + 29*x^19 + 36*x^18 + 27*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 7*x^11 + 20*x^10 + 49*x^9 + 70*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 98*x^4 + 59*x^3 + 76*x^2 + 109*x + 38, x^95 + 15*x^93 + 50*x^92 + 53*x^91 + 68*x^90 + 115*x^89 + 38*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 18*x^84 + 9*x^83 + 92*x^82 + 111*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 115*x^75 + 12*x^74 + 69*x^73 + 26*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 62*x^68 + 119*x^67 + 20*x^66 + 49*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 105*x^27 + 20*x^26 + 95*x^25 + 62*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 26*x^20 + 109*x^19 + 12*x^18 + 107*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 87*x^11 + 92*x^10 + x^9 + 18*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 38*x^4 + 43*x^3 + 68*x^2 + 93*x + 50, x^95 + 15*x^93 + 62*x^92 + 5*x^91 + 108*x^90 + 99*x^89 + 90*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 126*x^84 + 121*x^83 + 52*x^82 + 63*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 99*x^75 + 4*x^74 + 21*x^73 + 38*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 114*x^68 + 71*x^67 + 28*x^66 + 33*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 121*x^27 + 92*x^26 + 15*x^25 + 66*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 54*x^20 + 29*x^19 + 68*x^18 + 123*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 7*x^11 + 116*x^10 + 17*x^9 + 46*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 74*x^4 + 59*x^3 + 44*x^2 + 13*x + 46, x^95 + 15*x^93 + 114*x^92 + 85*x^91 + 36*x^90 + 83*x^89 + 6*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 18*x^84 + 105*x^83 + 124*x^82 + 15*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 83*x^75 + 44*x^74 + 101*x^73 + 58*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 62*x^68 + 23*x^67 + 116*x^66 + 17*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 9*x^27 + 116*x^26 + 63*x^25 + 30*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 26*x^20 + 77*x^19 + 44*x^18 + 11*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 55*x^11 + 124*x^10 + 33*x^9 + 50*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 38*x^4 + 75*x^3 + 36*x^2 + 61*x + 18, x^95 + 15*x^93 + 74*x^92 + 5*x^91 + 116*x^90 + 3*x^89 + 78*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 106*x^84 + 121*x^83 + 44*x^82 + 31*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 99*x^75 + 28*x^74 + 117*x^73 + 114*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 38*x^68 + 71*x^67 + 4*x^66 + 65*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 121*x^27 + 4*x^26 + 47*x^25 + 6*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 82*x^20 + 29*x^19 + 28*x^18 + 91*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 7*x^11 + 44*x^10 + 113*x^9 + 10*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 110*x^4 + 59*x^3 + 116*x^2 + 45*x + 106, x^95 + 15*x^93 + 74*x^92 + 37*x^91 + 116*x^90 + 99*x^89 + 78*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 106*x^84 + 89*x^83 + 44*x^82 + 63*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 67*x^75 + 28*x^74 + 21*x^73 + 114*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 38*x^68 + 103*x^67 + 4*x^66 + 33*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 25*x^27 + 4*x^26 + 15*x^25 + 6*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 82*x^20 + 125*x^19 + 28*x^18 + 123*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 103*x^11 + 44*x^10 + 17*x^9 + 10*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 110*x^4 + 91*x^3 + 116*x^2 + 13*x + 106, x^95 + 15*x^93 + 66*x^92 + 117*x^91 + 36*x^90 + 51*x^89 + 22*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 34*x^84 + 73*x^83 + 124*x^82 + 47*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 51*x^75 + 44*x^74 + 5*x^73 + 42*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 46*x^68 + 55*x^67 + 116*x^66 + 113*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 41*x^27 + 116*x^26 + 31*x^25 + 110*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 106*x^20 + 45*x^19 + 44*x^18 + 43*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 23*x^11 + 124*x^10 + 65*x^9 + 98*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 86*x^4 + 107*x^3 + 36*x^2 + 29*x + 2, x^95 + 15*x^93 + 70*x^92 + 53*x^91 + 28*x^90 + 19*x^89 + 114*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 6*x^84 + 9*x^83 + 4*x^82 + 79*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 115*x^75 + 20*x^74 + 37*x^73 + 14*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 42*x^68 + 119*x^67 + 12*x^66 + 81*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 105*x^27 + 76*x^26 + 127*x^25 + 58*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 94*x^20 + 109*x^19 + 84*x^18 + 75*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 87*x^11 + 68*x^10 + 97*x^9 + 118*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 34*x^4 + 43*x^3 + 92*x^2 + 125*x + 118, x^95 + 15*x^93 + 122*x^92 + 69*x^91 + 116*x^90 + 3*x^89 + 126*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 90*x^84 + 57*x^83 + 44*x^82 + 31*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 35*x^75 + 28*x^74 + 117*x^73 + 66*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 54*x^68 + 7*x^67 + 4*x^66 + 65*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 57*x^27 + 4*x^26 + 47*x^25 + 118*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 2*x^20 + 93*x^19 + 28*x^18 + 91*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 71*x^11 + 44*x^10 + 113*x^9 + 26*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 62*x^4 + 123*x^3 + 116*x^2 + 45*x + 58, x^95 + 15*x^93 + 10*x^92 + 69*x^91 + 52*x^90 + 67*x^89 + 78*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 42*x^84 + 57*x^83 + 108*x^82 + 95*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 35*x^75 + 92*x^74 + 53*x^73 + 114*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 102*x^68 + 7*x^67 + 68*x^66 + x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 57*x^27 + 68*x^26 + 111*x^25 + 6*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 18*x^20 + 93*x^19 + 92*x^18 + 27*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 71*x^11 + 108*x^10 + 49*x^9 + 10*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 46*x^4 + 123*x^3 + 52*x^2 + 109*x + 106, x^95 + 15*x^93 + 2*x^92 + 85*x^91 + 36*x^90 + 83*x^89 + 86*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 98*x^84 + 105*x^83 + 124*x^82 + 15*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 83*x^75 + 44*x^74 + 101*x^73 + 106*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 110*x^68 + 23*x^67 + 116*x^66 + 17*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 9*x^27 + 116*x^26 + 63*x^25 + 46*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 42*x^20 + 77*x^19 + 44*x^18 + 11*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 55*x^11 + 124*x^10 + 33*x^9 + 34*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 22*x^4 + 75*x^3 + 36*x^2 + 61*x + 66, x^95 + 15*x^93 + 86*x^92 + 85*x^91 + 92*x^90 + 51*x^89 + 66*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 86*x^84 + 105*x^83 + 68*x^82 + 47*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 83*x^75 + 84*x^74 + 5*x^73 + 62*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 90*x^68 + 23*x^67 + 76*x^66 + 113*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 9*x^27 + 12*x^26 + 31*x^25 + 74*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 110*x^20 + 77*x^19 + 20*x^18 + 43*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 55*x^11 + 4*x^10 + 65*x^9 + 102*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 18*x^4 + 75*x^3 + 28*x^2 + 29*x + 38, x^95 + 15*x^93 + 102*x^92 + 37*x^91 + 44*x^90 + 99*x^89 + 2*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 70*x^84 + 89*x^83 + 52*x^82 + 63*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 67*x^75 + 68*x^74 + 21*x^73 + 62*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 42*x^68 + 103*x^67 + 28*x^66 + 33*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 25*x^27 + 28*x^26 + 15*x^25 + 10*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 30*x^20 + 125*x^19 + 68*x^18 + 123*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 103*x^11 + 52*x^10 + 17*x^9 + 102*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 34*x^4 + 91*x^3 + 44*x^2 + 13*x + 6, x^95 + 15*x^93 + 14*x^92 + 85*x^91 + 28*x^90 + 19*x^89 + 122*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 110*x^84 + 105*x^83 + 68*x^82 + 79*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 83*x^75 + 20*x^74 + 37*x^73 + 70*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 66*x^68 + 23*x^67 + 76*x^66 + 81*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 9*x^27 + 76*x^26 + 127*x^25 + 98*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 102*x^20 + 77*x^19 + 20*x^18 + 75*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 55*x^11 + 68*x^10 + 97*x^9 + 78*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 90*x^4 + 75*x^3 + 28*x^2 + 125*x + 110, x^95 + 15*x^93 + 10*x^92 + 85*x^91 + 36*x^90 + 115*x^89 + 94*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 10*x^84 + 105*x^83 + 60*x^82 + 111*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 83*x^75 + 44*x^74 + 69*x^73 + 34*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 70*x^68 + 23*x^67 + 52*x^66 + 49*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 9*x^27 + 116*x^26 + 95*x^25 + 86*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 114*x^20 + 77*x^19 + 108*x^18 + 107*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 55*x^11 + 124*x^10 + x^9 + 122*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 14*x^4 + 75*x^3 + 100*x^2 + 93*x + 58, x^95 + 15*x^93 + 82*x^92 + 53*x^91 + 100*x^90 + 115*x^89 + 38*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 114*x^84 + 9*x^83 + 60*x^82 + 111*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 115*x^75 + 108*x^74 + 69*x^73 + 26*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 94*x^68 + 119*x^67 + 52*x^66 + 49*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 105*x^27 + 52*x^26 + 95*x^25 + 62*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 122*x^20 + 109*x^19 + 108*x^18 + 107*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 87*x^11 + 60*x^10 + x^9 + 18*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 70*x^4 + 43*x^3 + 100*x^2 + 93*x + 114, x^95 + 15*x^93 + 46*x^92 + 5*x^91 + 76*x^90 + 35*x^89 + 106*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 110*x^84 + 121*x^83 + 84*x^82 + 127*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 99*x^75 + 36*x^74 + 85*x^73 + 22*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 2*x^68 + 71*x^67 + 124*x^66 + 97*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 121*x^27 + 60*x^26 + 79*x^25 + 18*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 102*x^20 + 29*x^19 + 100*x^18 + 59*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 7*x^11 + 20*x^10 + 81*x^9 + 94*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 26*x^4 + 59*x^3 + 12*x^2 + 77*x + 94, x^95 + 15*x^93 + 110*x^92 + 53*x^91 + 60*x^90 + 115*x^89 + 122*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 14*x^84 + 9*x^83 + 36*x^82 + 111*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 115*x^75 + 116*x^74 + 69*x^73 + 70*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 34*x^68 + 119*x^67 + 108*x^66 + 49*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 105*x^27 + 108*x^26 + 95*x^25 + 98*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 6*x^20 + 109*x^19 + 116*x^18 + 107*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 87*x^11 + 36*x^10 + x^9 + 78*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 58*x^4 + 43*x^3 + 60*x^2 + 93*x + 46, x^95 + 15*x^93 + 70*x^92 + 117*x^91 + 92*x^90 + 83*x^89 + 50*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 6*x^84 + 73*x^83 + 68*x^82 + 15*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 51*x^75 + 84*x^74 + 101*x^73 + 78*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 42*x^68 + 55*x^67 + 76*x^66 + 17*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 41*x^27 + 12*x^26 + 63*x^25 + 122*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 94*x^20 + 45*x^19 + 20*x^18 + 11*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 23*x^11 + 4*x^10 + 33*x^9 + 54*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 34*x^4 + 107*x^3 + 28*x^2 + 61*x + 54, x^95 + 15*x^93 + 90*x^92 + 101*x^91 + 116*x^90 + 99*x^89 + 94*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 58*x^84 + 25*x^83 + 44*x^82 + 63*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 3*x^75 + 28*x^74 + 21*x^73 + 98*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 86*x^68 + 39*x^67 + 4*x^66 + 33*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 89*x^27 + 4*x^26 + 15*x^25 + 86*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 98*x^20 + 61*x^19 + 28*x^18 + 123*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 39*x^11 + 44*x^10 + 17*x^9 + 58*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 94*x^4 + 27*x^3 + 116*x^2 + 13*x + 90, x^95 + 15*x^93 + 6*x^92 + 21*x^91 + 60*x^90 + 115*x^89 + 82*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 6*x^84 + 41*x^83 + 100*x^82 + 111*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 19*x^75 + 116*x^74 + 69*x^73 + 46*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 42*x^68 + 87*x^67 + 44*x^66 + 49*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 73*x^27 + 108*x^26 + 95*x^25 + 26*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 94*x^20 + 13*x^19 + 52*x^18 + 107*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 119*x^11 + 36*x^10 + x^9 + 22*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 34*x^4 + 11*x^3 + 124*x^2 + 93*x + 86, x^95 + 15*x^93 + 26*x^92 + 53*x^91 + 100*x^90 + 83*x^89 + 46*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 90*x^84 + 9*x^83 + 124*x^82 + 15*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 115*x^75 + 108*x^74 + 101*x^73 + 82*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 118*x^68 + 119*x^67 + 116*x^66 + 17*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 105*x^27 + 52*x^26 + 63*x^25 + 102*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 2*x^20 + 109*x^19 + 44*x^18 + 11*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 87*x^11 + 60*x^10 + 33*x^9 + 106*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 126*x^4 + 43*x^3 + 36*x^2 + 61*x + 106, x^95 + 15*x^93 + 66*x^92 + 21*x^91 + 36*x^90 + 19*x^89 + 22*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 34*x^84 + 41*x^83 + 124*x^82 + 79*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 19*x^75 + 44*x^74 + 37*x^73 + 42*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 46*x^68 + 87*x^67 + 116*x^66 + 81*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 73*x^27 + 116*x^26 + 127*x^25 + 110*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 106*x^20 + 13*x^19 + 44*x^18 + 75*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 119*x^11 + 124*x^10 + 97*x^9 + 98*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 86*x^4 + 11*x^3 + 36*x^2 + 125*x + 2, x^95 + 15*x^93 + 70*x^92 + 53*x^91 + 60*x^90 + 83*x^89 + 18*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 70*x^84 + 9*x^83 + 100*x^82 + 15*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 115*x^75 + 116*x^74 + 101*x^73 + 110*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 106*x^68 + 119*x^67 + 44*x^66 + 17*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 105*x^27 + 108*x^26 + 63*x^25 + 90*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 30*x^20 + 109*x^19 + 52*x^18 + 11*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 87*x^11 + 36*x^10 + 33*x^9 + 86*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 98*x^4 + 43*x^3 + 124*x^2 + 61*x + 22, x^95 + 15*x^93 + 126*x^92 + 5*x^91 + 44*x^90 + 35*x^89 + 26*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 62*x^84 + 121*x^83 + 116*x^82 + 127*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 99*x^75 + 68*x^74 + 85*x^73 + 102*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 50*x^68 + 71*x^67 + 92*x^66 + 97*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 121*x^27 + 28*x^26 + 79*x^25 + 2*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 118*x^20 + 29*x^19 + 4*x^18 + 59*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 7*x^11 + 52*x^10 + 81*x^9 + 110*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 10*x^4 + 59*x^3 + 108*x^2 + 77*x + 110, x^95 + 15*x^93 + 102*x^92 + 37*x^91 + 108*x^90 + 99*x^89 + 66*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 70*x^84 + 89*x^83 + 116*x^82 + 63*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 67*x^75 + 4*x^74 + 21*x^73 + 126*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 42*x^68 + 103*x^67 + 92*x^66 + 33*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 25*x^27 + 92*x^26 + 15*x^25 + 74*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 30*x^20 + 125*x^19 + 4*x^18 + 123*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 103*x^11 + 116*x^10 + 17*x^9 + 38*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 34*x^4 + 91*x^3 + 108*x^2 + 13*x + 70, x^95 + 15*x^93 + 106*x^92 + 37*x^91 + 52*x^90 + 99*x^89 + 46*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 10*x^84 + 89*x^83 + 108*x^82 + 63*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 67*x^75 + 92*x^74 + 21*x^73 + 18*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 6*x^68 + 103*x^67 + 68*x^66 + 33*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 25*x^27 + 68*x^26 + 15*x^25 + 102*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 114*x^20 + 125*x^19 + 92*x^18 + 123*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 103*x^11 + 108*x^10 + 17*x^9 + 42*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 78*x^4 + 91*x^3 + 52*x^2 + 13*x + 10, x^95 + 15*x^93 + 102*x^92 + 53*x^91 + 28*x^90 + 19*x^89 + 18*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 38*x^84 + 9*x^83 + 4*x^82 + 79*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 115*x^75 + 20*x^74 + 37*x^73 + 110*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 10*x^68 + 119*x^67 + 12*x^66 + 81*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 105*x^27 + 76*x^26 + 127*x^25 + 90*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 126*x^20 + 109*x^19 + 84*x^18 + 75*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 87*x^11 + 68*x^10 + 97*x^9 + 86*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 2*x^4 + 43*x^3 + 92*x^2 + 125*x + 86, x^95 + 15*x^93 + 46*x^92 + 21*x^91 + 124*x^90 + 19*x^89 + 122*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 78*x^84 + 41*x^83 + 100*x^82 + 79*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 19*x^75 + 52*x^74 + 37*x^73 + 70*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 98*x^68 + 87*x^67 + 44*x^66 + 81*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 73*x^27 + 44*x^26 + 127*x^25 + 98*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 70*x^20 + 13*x^19 + 52*x^18 + 75*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 119*x^11 + 100*x^10 + 97*x^9 + 78*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 122*x^4 + 11*x^3 + 124*x^2 + 125*x + 46, x^95 + 15*x^93 + 114*x^92 + 85*x^91 + 68*x^90 + 19*x^89 + 38*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 82*x^84 + 105*x^83 + 92*x^82 + 79*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 83*x^75 + 12*x^74 + 37*x^73 + 26*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 126*x^68 + 23*x^67 + 20*x^66 + 81*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 9*x^27 + 20*x^26 + 127*x^25 + 62*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 90*x^20 + 77*x^19 + 12*x^18 + 75*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 55*x^11 + 92*x^10 + 97*x^9 + 18*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 102*x^4 + 75*x^3 + 68*x^2 + 125*x + 50, x^95 + 15*x^93 + 62*x^92 + 53*x^91 + 60*x^90 + 115*x^89 + 10*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 30*x^84 + 9*x^83 + 36*x^82 + 111*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 115*x^75 + 116*x^74 + 69*x^73 + 54*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 18*x^68 + 119*x^67 + 108*x^66 + 49*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 105*x^27 + 108*x^26 + 95*x^25 + 50*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 86*x^20 + 109*x^19 + 116*x^18 + 107*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 87*x^11 + 36*x^10 + x^9 + 126*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 106*x^4 + 43*x^3 + 60*x^2 + 93*x + 30, x^95 + 15*x^93 + 22*x^92 + 117*x^91 + 28*x^90 + 19*x^89 + 66*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 22*x^84 + 73*x^83 + 4*x^82 + 79*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 51*x^75 + 20*x^74 + 37*x^73 + 62*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 26*x^68 + 55*x^67 + 12*x^66 + 81*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 41*x^27 + 76*x^26 + 127*x^25 + 74*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 46*x^20 + 45*x^19 + 84*x^18 + 75*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 23*x^11 + 68*x^10 + 97*x^9 + 102*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 82*x^4 + 107*x^3 + 92*x^2 + 125*x + 38, x^95 + 15*x^93 + 66*x^92 + 117*x^91 + 36*x^90 + 115*x^89 + 86*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 34*x^84 + 73*x^83 + 124*x^82 + 111*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 51*x^75 + 44*x^74 + 69*x^73 + 106*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 46*x^68 + 55*x^67 + 116*x^66 + 49*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 41*x^27 + 116*x^26 + 95*x^25 + 46*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 106*x^20 + 45*x^19 + 44*x^18 + 107*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 23*x^11 + 124*x^10 + x^9 + 34*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 86*x^4 + 107*x^3 + 36*x^2 + 93*x + 66, x^95 + 15*x^93 + 114*x^92 + 53*x^91 + 36*x^90 + 51*x^89 + 70*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 18*x^84 + 9*x^83 + 124*x^82 + 47*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 115*x^75 + 44*x^74 + 5*x^73 + 122*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 62*x^68 + 119*x^67 + 116*x^66 + 113*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 105*x^27 + 116*x^26 + 31*x^25 + 94*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 26*x^20 + 109*x^19 + 44*x^18 + 43*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 87*x^11 + 124*x^10 + 65*x^9 + 114*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 38*x^4 + 43*x^3 + 36*x^2 + 29*x + 82, x^95 + 15*x^93 + 14*x^92 + 117*x^91 + 92*x^90 + 115*x^89 + 58*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 110*x^84 + 73*x^83 + 4*x^82 + 111*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 51*x^75 + 84*x^74 + 69*x^73 + 6*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 66*x^68 + 55*x^67 + 12*x^66 + 49*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 41*x^27 + 12*x^26 + 95*x^25 + 34*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 102*x^20 + 45*x^19 + 84*x^18 + 107*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 23*x^11 + 4*x^10 + x^9 + 14*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 90*x^4 + 107*x^3 + 92*x^2 + 93*x + 46, x^95 + 15*x^93 + 70*x^92 + 5*x^91 + 12*x^90 + 67*x^89 + 66*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 102*x^84 + 121*x^83 + 84*x^82 + 95*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 99*x^75 + 100*x^74 + 53*x^73 + 126*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 10*x^68 + 71*x^67 + 124*x^66 + x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 121*x^27 + 124*x^26 + 111*x^25 + 74*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 62*x^20 + 29*x^19 + 100*x^18 + 27*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 7*x^11 + 84*x^10 + 49*x^9 + 38*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 2*x^4 + 59*x^3 + 12*x^2 + 109*x + 6, x^95 + 15*x^93 + 66*x^92 + 5*x^91 + 84*x^90 + 99*x^89 + 102*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 2*x^84 + 121*x^83 + 12*x^82 + 63*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 99*x^75 + 60*x^74 + 21*x^73 + 26*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 14*x^68 + 71*x^67 + 36*x^66 + 33*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 121*x^27 + 100*x^26 + 15*x^25 + 126*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 74*x^20 + 29*x^19 + 124*x^18 + 123*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 7*x^11 + 76*x^10 + 17*x^9 + 18*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 54*x^4 + 59*x^3 + 20*x^2 + 13*x + 18, x^95 + 15*x^93 + 126*x^92 + 21*x^91 + 60*x^90 + 19*x^89 + 74*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 94*x^84 + 41*x^83 + 36*x^82 + 79*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 19*x^75 + 116*x^74 + 37*x^73 + 118*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 82*x^68 + 87*x^67 + 108*x^66 + 81*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 73*x^27 + 108*x^26 + 127*x^25 + 114*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 22*x^20 + 13*x^19 + 116*x^18 + 75*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 119*x^11 + 36*x^10 + 97*x^9 + 62*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 42*x^4 + 11*x^3 + 60*x^2 + 125*x + 94, x^95 + 15*x^93 + 38*x^92 + 101*x^91 + 12*x^90 + 99*x^89 + 34*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 70*x^84 + 25*x^83 + 84*x^82 + 63*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 3*x^75 + 100*x^74 + 21*x^73 + 30*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 42*x^68 + 39*x^67 + 124*x^66 + 33*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 89*x^27 + 124*x^26 + 15*x^25 + 42*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 30*x^20 + 61*x^19 + 100*x^18 + 123*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 39*x^11 + 84*x^10 + 17*x^9 + 70*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 34*x^4 + 27*x^3 + 12*x^2 + 13*x + 38, x^95 + 15*x^93 + 10*x^92 + 5*x^91 + 84*x^90 + 3*x^89 + 46*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 106*x^84 + 121*x^83 + 76*x^82 + 31*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 99*x^75 + 60*x^74 + 117*x^73 + 18*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 38*x^68 + 71*x^67 + 100*x^66 + 65*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 121*x^27 + 100*x^26 + 47*x^25 + 102*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 82*x^20 + 29*x^19 + 60*x^18 + 91*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 7*x^11 + 76*x^10 + 113*x^9 + 42*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 110*x^4 + 59*x^3 + 84*x^2 + 45*x + 74, x^95 + 15*x^93 + 26*x^92 + 37*x^91 + 84*x^90 + 99*x^89 + 126*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 58*x^84 + 89*x^83 + 76*x^82 + 63*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 67*x^75 + 60*x^74 + 21*x^73 + 66*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 86*x^68 + 103*x^67 + 100*x^66 + 33*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 25*x^27 + 100*x^26 + 15*x^25 + 118*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 98*x^20 + 125*x^19 + 60*x^18 + 123*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 103*x^11 + 76*x^10 + 17*x^9 + 26*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 94*x^4 + 91*x^3 + 84*x^2 + 13*x + 122, x^95 + 15*x^93 + 50*x^92 + 69*x^91 + 20*x^90 + 35*x^89 + 86*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 50*x^84 + 57*x^83 + 76*x^82 + 127*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 35*x^75 + 124*x^74 + 85*x^73 + 42*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 94*x^68 + 7*x^67 + 100*x^66 + 97*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 57*x^27 + 36*x^26 + 79*x^25 + 46*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 58*x^20 + 93*x^19 + 60*x^18 + 59*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 71*x^11 + 12*x^10 + 81*x^9 + 98*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 70*x^4 + 123*x^3 + 84*x^2 + 77*x + 34, x^95 + 15*x^93 + 54*x^92 + 69*x^91 + 76*x^90 + 67*x^89 + 114*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 22*x^84 + 57*x^83 + 20*x^82 + 95*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 35*x^75 + 36*x^74 + 53*x^73 + 78*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 90*x^68 + 7*x^67 + 60*x^66 + x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 57*x^27 + 60*x^26 + 111*x^25 + 58*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 46*x^20 + 93*x^19 + 36*x^18 + 27*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 71*x^11 + 20*x^10 + 49*x^9 + 54*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 18*x^4 + 123*x^3 + 76*x^2 + 109*x + 86, x^95 + 15*x^93 + 14*x^92 + 5*x^91 + 44*x^90 + 35*x^89 + 106*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 14*x^84 + 121*x^83 + 116*x^82 + 127*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 99*x^75 + 68*x^74 + 85*x^73 + 22*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 98*x^68 + 71*x^67 + 92*x^66 + 97*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 121*x^27 + 28*x^26 + 79*x^25 + 18*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 6*x^20 + 29*x^19 + 4*x^18 + 59*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 7*x^11 + 52*x^10 + 81*x^9 + 94*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 122*x^4 + 59*x^3 + 108*x^2 + 77*x + 30, x^95 + 15*x^93 + 14*x^92 + 21*x^91 + 28*x^90 + 83*x^89 + 122*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 110*x^84 + 41*x^83 + 68*x^82 + 15*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 19*x^75 + 20*x^74 + 101*x^73 + 70*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 66*x^68 + 87*x^67 + 76*x^66 + 17*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 73*x^27 + 76*x^26 + 63*x^25 + 98*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 102*x^20 + 13*x^19 + 20*x^18 + 11*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 119*x^11 + 68*x^10 + 33*x^9 + 78*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 90*x^4 + 11*x^3 + 28*x^2 + 61*x + 110, x^95 + 15*x^93 + 82*x^92 + 53*x^91 + 68*x^90 + 51*x^89 + 6*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 50*x^84 + 9*x^83 + 92*x^82 + 47*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 115*x^75 + 12*x^74 + 5*x^73 + 58*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 30*x^68 + 119*x^67 + 20*x^66 + 113*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 105*x^27 + 20*x^26 + 31*x^25 + 30*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 58*x^20 + 109*x^19 + 12*x^18 + 43*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 87*x^11 + 92*x^10 + 65*x^9 + 50*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 6*x^4 + 43*x^3 + 68*x^2 + 29*x + 82, x^95 + 15*x^93 + 122*x^92 + 53*x^91 + 4*x^90 + 83*x^89 + 110*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 122*x^84 + 9*x^83 + 92*x^82 + 15*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 115*x^75 + 76*x^74 + 101*x^73 + 18*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 86*x^68 + 119*x^67 + 20*x^66 + 17*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 105*x^27 + 84*x^26 + 63*x^25 + 38*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 34*x^20 + 109*x^19 + 12*x^18 + 11*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 87*x^11 + 28*x^10 + 33*x^9 + 42*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 94*x^4 + 43*x^3 + 68*x^2 + 61*x + 106, x^95 + 15*x^93 + 54*x^92 + 37*x^91 + 108*x^90 + 35*x^89 + 18*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 86*x^84 + 89*x^83 + 116*x^82 + 127*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 67*x^75 + 4*x^74 + 85*x^73 + 46*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 26*x^68 + 103*x^67 + 92*x^66 + 97*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 25*x^27 + 92*x^26 + 79*x^25 + 90*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 110*x^20 + 125*x^19 + 4*x^18 + 59*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 103*x^11 + 116*x^10 + 81*x^9 + 22*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 82*x^4 + 91*x^3 + 108*x^2 + 77*x + 118, x^95 + 15*x^93 + 30*x^92 + 37*x^91 + 12*x^90 + 67*x^89 + 26*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 30*x^84 + 89*x^83 + 20*x^82 + 95*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 67*x^75 + 100*x^74 + 53*x^73 + 102*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 82*x^68 + 103*x^67 + 60*x^66 + x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 25*x^27 + 124*x^26 + 111*x^25 + 2*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 86*x^20 + 125*x^19 + 36*x^18 + 27*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 103*x^11 + 84*x^10 + 49*x^9 + 110*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 42*x^4 + 91*x^3 + 76*x^2 + 109*x + 46, x^95 + 15*x^93 + 34*x^92 + 5*x^91 + 20*x^90 + 99*x^89 + 6*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 98*x^84 + 121*x^83 + 76*x^82 + 63*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 99*x^75 + 124*x^74 + 21*x^73 + 122*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 46*x^68 + 71*x^67 + 100*x^66 + 33*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 121*x^27 + 36*x^26 + 15*x^25 + 30*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 42*x^20 + 29*x^19 + 60*x^18 + 123*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 7*x^11 + 12*x^10 + 17*x^9 + 114*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 86*x^4 + 59*x^3 + 84*x^2 + 13*x + 114, x^95 + 15*x^93 + 90*x^92 + 37*x^91 + 84*x^90 + 35*x^89 + 126*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 122*x^84 + 89*x^83 + 76*x^82 + 127*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 67*x^75 + 60*x^74 + 85*x^73 + 66*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 22*x^68 + 103*x^67 + 100*x^66 + 97*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 25*x^27 + 100*x^26 + 79*x^25 + 118*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 34*x^20 + 125*x^19 + 60*x^18 + 59*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 103*x^11 + 76*x^10 + 81*x^9 + 26*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 30*x^4 + 91*x^3 + 84*x^2 + 77*x + 122, x^95 + 15*x^93 + 70*x^92 + 37*x^91 + 44*x^90 + 99*x^89 + 98*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 38*x^84 + 89*x^83 + 52*x^82 + 63*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 67*x^75 + 68*x^74 + 21*x^73 + 94*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 74*x^68 + 103*x^67 + 28*x^66 + 33*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 25*x^27 + 28*x^26 + 15*x^25 + 106*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 126*x^20 + 125*x^19 + 68*x^18 + 123*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 103*x^11 + 52*x^10 + 17*x^9 + 6*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 66*x^4 + 91*x^3 + 44*x^2 + 13*x + 38, x^95 + 15*x^93 + 86*x^92 + 117*x^91 + 124*x^90 + 83*x^89 + 98*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 22*x^84 + 73*x^83 + 36*x^82 + 15*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 51*x^75 + 52*x^74 + 101*x^73 + 30*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 26*x^68 + 55*x^67 + 108*x^66 + 17*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 41*x^27 + 44*x^26 + 63*x^25 + 106*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 46*x^20 + 45*x^19 + 116*x^18 + 11*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 23*x^11 + 100*x^10 + 33*x^9 + 70*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 82*x^4 + 107*x^3 + 60*x^2 + 61*x + 70, x^95 + 15*x^93 + 102*x^92 + 101*x^91 + 108*x^90 + 99*x^89 + 2*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 70*x^84 + 25*x^83 + 116*x^82 + 63*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 3*x^75 + 4*x^74 + 21*x^73 + 62*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 42*x^68 + 39*x^67 + 92*x^66 + 33*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 89*x^27 + 92*x^26 + 15*x^25 + 10*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 30*x^20 + 61*x^19 + 4*x^18 + 123*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 39*x^11 + 116*x^10 + 17*x^9 + 102*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 34*x^4 + 27*x^3 + 108*x^2 + 13*x + 6, x^95 + 15*x^93 + 22*x^92 + 85*x^91 + 92*x^90 + 51*x^89 + 2*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 22*x^84 + 105*x^83 + 68*x^82 + 47*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 83*x^75 + 84*x^74 + 5*x^73 + 126*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 26*x^68 + 23*x^67 + 76*x^66 + 113*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 9*x^27 + 12*x^26 + 31*x^25 + 10*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 46*x^20 + 77*x^19 + 20*x^18 + 43*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 55*x^11 + 4*x^10 + 65*x^9 + 38*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 82*x^4 + 75*x^3 + 28*x^2 + 29*x + 102, x^95 + 15*x^93 + 90*x^92 + 101*x^91 + 84*x^90 + 99*x^89 + 126*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 122*x^84 + 25*x^83 + 76*x^82 + 63*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 3*x^75 + 60*x^74 + 21*x^73 + 66*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 22*x^68 + 39*x^67 + 100*x^66 + 33*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 89*x^27 + 100*x^26 + 15*x^25 + 118*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 34*x^20 + 61*x^19 + 60*x^18 + 123*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 39*x^11 + 76*x^10 + 17*x^9 + 26*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 30*x^4 + 27*x^3 + 84*x^2 + 13*x + 122, x^95 + 15*x^93 + 94*x^92 + 117*x^91 + 124*x^90 + 51*x^89 + 106*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 62*x^84 + 73*x^83 + 100*x^82 + 47*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 51*x^75 + 52*x^74 + 5*x^73 + 86*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 114*x^68 + 55*x^67 + 44*x^66 + 113*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 41*x^27 + 44*x^26 + 31*x^25 + 18*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 118*x^20 + 45*x^19 + 52*x^18 + 43*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 23*x^11 + 100*x^10 + 65*x^9 + 30*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 74*x^4 + 107*x^3 + 124*x^2 + 29*x + 62, x^95 + 15*x^93 + 110*x^92 + 69*x^91 + 108*x^90 + 99*x^89 + 10*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 110*x^84 + 57*x^83 + 52*x^82 + 63*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 35*x^75 + 4*x^74 + 21*x^73 + 118*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 2*x^68 + 7*x^67 + 28*x^66 + 33*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 57*x^27 + 92*x^26 + 15*x^25 + 50*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 102*x^20 + 93*x^19 + 68*x^18 + 123*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 71*x^11 + 116*x^10 + 17*x^9 + 62*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 26*x^4 + 123*x^3 + 44*x^2 + 13*x + 126, x^95 + 15*x^93 + 126*x^92 + 101*x^91 + 12*x^90 + 3*x^89 + 122*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 126*x^84 + 25*x^83 + 20*x^82 + 31*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 3*x^75 + 100*x^74 + 117*x^73 + 6*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 114*x^68 + 39*x^67 + 60*x^66 + 65*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 89*x^27 + 124*x^26 + 47*x^25 + 98*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 54*x^20 + 61*x^19 + 36*x^18 + 91*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 39*x^11 + 84*x^10 + 113*x^9 + 14*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 74*x^4 + 27*x^3 + 76*x^2 + 45*x + 78, x^95 + 15*x^93 + 62*x^92 + 37*x^91 + 12*x^90 + 3*x^89 + 122*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 62*x^84 + 89*x^83 + 20*x^82 + 31*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 67*x^75 + 100*x^74 + 117*x^73 + 6*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 50*x^68 + 103*x^67 + 60*x^66 + 65*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 25*x^27 + 124*x^26 + 47*x^25 + 98*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 118*x^20 + 125*x^19 + 36*x^18 + 91*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 103*x^11 + 84*x^10 + 113*x^9 + 14*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 10*x^4 + 91*x^3 + 76*x^2 + 45*x + 78, x^95 + 15*x^93 + 26*x^92 + 117*x^91 + 68*x^90 + 83*x^89 + 14*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 26*x^84 + 73*x^83 + 28*x^82 + 15*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 51*x^75 + 12*x^74 + 101*x^73 + 114*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 54*x^68 + 55*x^67 + 84*x^66 + 17*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 41*x^27 + 20*x^26 + 63*x^25 + 70*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 66*x^20 + 45*x^19 + 76*x^18 + 11*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 23*x^11 + 92*x^10 + 33*x^9 + 10*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 62*x^4 + 107*x^3 + 4*x^2 + 61*x + 74, x^95 + 15*x^93 + 102*x^92 + 117*x^91 + 124*x^90 + 83*x^89 + 50*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 102*x^84 + 73*x^83 + 36*x^82 + 15*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 51*x^75 + 52*x^74 + 101*x^73 + 78*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 74*x^68 + 55*x^67 + 108*x^66 + 17*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 41*x^27 + 44*x^26 + 63*x^25 + 122*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 62*x^20 + 45*x^19 + 116*x^18 + 11*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 23*x^11 + 100*x^10 + 33*x^9 + 54*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 66*x^4 + 107*x^3 + 60*x^2 + 61*x + 118, x^95 + 15*x^93 + 62*x^92 + 117*x^91 + 92*x^90 + 115*x^89 + 42*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 94*x^84 + 73*x^83 + 4*x^82 + 111*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 51*x^75 + 84*x^74 + 69*x^73 + 22*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 82*x^68 + 55*x^67 + 12*x^66 + 49*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 41*x^27 + 12*x^26 + 95*x^25 + 82*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 22*x^20 + 45*x^19 + 84*x^18 + 107*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 23*x^11 + 4*x^10 + x^9 + 94*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 42*x^4 + 107*x^3 + 92*x^2 + 93*x + 62, x^95 + 15*x^93 + 94*x^92 + 37*x^91 + 108*x^90 + 67*x^89 + 122*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 30*x^84 + 89*x^83 + 52*x^82 + 95*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 67*x^75 + 4*x^74 + 53*x^73 + 6*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 82*x^68 + 103*x^67 + 28*x^66 + x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 25*x^27 + 92*x^26 + 111*x^25 + 98*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 86*x^20 + 125*x^19 + 68*x^18 + 27*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 103*x^11 + 116*x^10 + 49*x^9 + 14*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 42*x^4 + 91*x^3 + 44*x^2 + 109*x + 14, x^95 + 15*x^93 + 10*x^92 + 69*x^91 + 84*x^90 + 67*x^89 + 46*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 106*x^84 + 57*x^83 + 76*x^82 + 95*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 35*x^75 + 60*x^74 + 53*x^73 + 18*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 38*x^68 + 7*x^67 + 100*x^66 + x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 57*x^27 + 100*x^26 + 111*x^25 + 102*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 82*x^20 + 93*x^19 + 60*x^18 + 27*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 71*x^11 + 76*x^10 + 49*x^9 + 42*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 110*x^4 + 123*x^3 + 84*x^2 + 109*x + 74, x^95 + 15*x^93 + 94*x^92 + 53*x^91 + 124*x^90 + 51*x^89 + 42*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 62*x^84 + 9*x^83 + 100*x^82 + 47*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 115*x^75 + 52*x^74 + 5*x^73 + 22*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 114*x^68 + 119*x^67 + 44*x^66 + 113*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 105*x^27 + 44*x^26 + 31*x^25 + 82*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 118*x^20 + 109*x^19 + 52*x^18 + 43*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 87*x^11 + 100*x^10 + 65*x^9 + 94*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 74*x^4 + 43*x^3 + 124*x^2 + 29*x + 126, x^95 + 15*x^93 + 82*x^92 + 37*x^91 + 52*x^90 + 3*x^89 + 22*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 18*x^84 + 89*x^83 + 44*x^82 + 31*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 67*x^75 + 92*x^74 + 117*x^73 + 106*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 126*x^68 + 103*x^67 + 4*x^66 + 65*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 25*x^27 + 68*x^26 + 47*x^25 + 110*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 26*x^20 + 125*x^19 + 28*x^18 + 91*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 103*x^11 + 108*x^10 + 113*x^9 + 34*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 102*x^4 + 91*x^3 + 116*x^2 + 45*x + 34, x^95 + 15*x^93 + 22*x^92 + 5*x^91 + 76*x^90 + 3*x^89 + 82*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 118*x^84 + 121*x^83 + 20*x^82 + 31*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 99*x^75 + 36*x^74 + 117*x^73 + 110*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 122*x^68 + 71*x^67 + 60*x^66 + 65*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 121*x^27 + 60*x^26 + 47*x^25 + 26*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 14*x^20 + 29*x^19 + 36*x^18 + 91*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 7*x^11 + 20*x^10 + 113*x^9 + 86*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 50*x^4 + 59*x^3 + 76*x^2 + 45*x + 118, x^95 + 15*x^93 + 2*x^92 + 117*x^91 + 100*x^90 + 51*x^89 + 22*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 98*x^84 + 73*x^83 + 60*x^82 + 47*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 51*x^75 + 108*x^74 + 5*x^73 + 42*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 110*x^68 + 55*x^67 + 52*x^66 + 113*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 41*x^27 + 52*x^26 + 31*x^25 + 110*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 42*x^20 + 45*x^19 + 108*x^18 + 43*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 23*x^11 + 60*x^10 + 65*x^9 + 98*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 22*x^4 + 107*x^3 + 100*x^2 + 29*x + 2, x^95 + 15*x^93 + 26*x^92 + 5*x^91 + 84*x^90 + 3*x^89 + 126*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 58*x^84 + 121*x^83 + 76*x^82 + 31*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 99*x^75 + 60*x^74 + 117*x^73 + 66*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 86*x^68 + 71*x^67 + 100*x^66 + 65*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 121*x^27 + 100*x^26 + 47*x^25 + 118*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 98*x^20 + 29*x^19 + 60*x^18 + 91*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 7*x^11 + 76*x^10 + 113*x^9 + 26*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 94*x^4 + 59*x^3 + 84*x^2 + 45*x + 122, x^95 + 15*x^93 + 78*x^92 + 85*x^91 + 60*x^90 + 19*x^89 + 26*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 110*x^84 + 105*x^83 + 36*x^82 + 79*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 83*x^75 + 116*x^74 + 37*x^73 + 38*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 66*x^68 + 23*x^67 + 108*x^66 + 81*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 9*x^27 + 108*x^26 + 127*x^25 + 2*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 102*x^20 + 77*x^19 + 116*x^18 + 75*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 55*x^11 + 36*x^10 + 97*x^9 + 46*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 90*x^4 + 75*x^3 + 60*x^2 + 125*x + 14, x^95 + 15*x^93 + 102*x^92 + 117*x^91 + 92*x^90 + 83*x^89 + 82*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 38*x^84 + 73*x^83 + 68*x^82 + 15*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 51*x^75 + 84*x^74 + 101*x^73 + 46*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 10*x^68 + 55*x^67 + 76*x^66 + 17*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 41*x^27 + 12*x^26 + 63*x^25 + 26*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 126*x^20 + 45*x^19 + 20*x^18 + 11*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 23*x^11 + 4*x^10 + 33*x^9 + 22*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 2*x^4 + 107*x^3 + 28*x^2 + 61*x + 22, x^95 + 15*x^93 + 102*x^92 + 69*x^91 + 108*x^90 + 67*x^89 + 66*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 70*x^84 + 57*x^83 + 116*x^82 + 95*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 35*x^75 + 4*x^74 + 53*x^73 + 126*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 42*x^68 + 7*x^67 + 92*x^66 + x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 57*x^27 + 92*x^26 + 111*x^25 + 74*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 30*x^20 + 93*x^19 + 4*x^18 + 27*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 71*x^11 + 116*x^10 + 49*x^9 + 38*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 34*x^4 + 123*x^3 + 108*x^2 + 109*x + 70, x^95 + 15*x^93 + 42*x^92 + 117*x^91 + 68*x^90 + 83*x^89 + 94*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 106*x^84 + 73*x^83 + 28*x^82 + 15*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 51*x^75 + 12*x^74 + 101*x^73 + 34*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 102*x^68 + 55*x^67 + 84*x^66 + 17*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 41*x^27 + 20*x^26 + 63*x^25 + 86*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 82*x^20 + 45*x^19 + 76*x^18 + 11*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 23*x^11 + 92*x^10 + 33*x^9 + 122*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 46*x^4 + 107*x^3 + 4*x^2 + 61*x + 122, x^95 + 15*x^93 + 82*x^92 + 101*x^91 + 52*x^90 + 67*x^89 + 22*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 18*x^84 + 25*x^83 + 44*x^82 + 95*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 3*x^75 + 92*x^74 + 53*x^73 + 106*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 126*x^68 + 39*x^67 + 4*x^66 + x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 89*x^27 + 68*x^26 + 111*x^25 + 110*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 26*x^20 + 61*x^19 + 28*x^18 + 27*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 39*x^11 + 108*x^10 + 49*x^9 + 34*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 102*x^4 + 27*x^3 + 116*x^2 + 109*x + 34, x^95 + 15*x^93 + 50*x^92 + 5*x^91 + 116*x^90 + 99*x^89 + 118*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 114*x^84 + 121*x^83 + 108*x^82 + 63*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 99*x^75 + 28*x^74 + 21*x^73 + 10*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 30*x^68 + 71*x^67 + 68*x^66 + 33*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 121*x^27 + 4*x^26 + 15*x^25 + 78*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 122*x^20 + 29*x^19 + 92*x^18 + 123*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 7*x^11 + 44*x^10 + 17*x^9 + 66*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 6*x^4 + 59*x^3 + 52*x^2 + 13*x + 66, x^95 + 15*x^93 + 2*x^92 + 37*x^91 + 52*x^90 + 67*x^89 + 70*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 2*x^84 + 89*x^83 + 44*x^82 + 95*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 67*x^75 + 92*x^74 + 53*x^73 + 58*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 14*x^68 + 103*x^67 + 4*x^66 + x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 25*x^27 + 68*x^26 + 111*x^25 + 94*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 74*x^20 + 125*x^19 + 28*x^18 + 27*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 103*x^11 + 108*x^10 + 49*x^9 + 50*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 54*x^4 + 91*x^3 + 116*x^2 + 109*x + 114, x^95 + 15*x^93 + 90*x^92 + 53*x^91 + 36*x^90 + 83*x^89 + 46*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 26*x^84 + 9*x^83 + 60*x^82 + 15*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 115*x^75 + 44*x^74 + 101*x^73 + 82*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 54*x^68 + 119*x^67 + 52*x^66 + 17*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 105*x^27 + 116*x^26 + 63*x^25 + 102*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 66*x^20 + 109*x^19 + 108*x^18 + 11*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 87*x^11 + 124*x^10 + 33*x^9 + 106*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 62*x^4 + 43*x^3 + 100*x^2 + 61*x + 106, x^95 + 15*x^93 + 38*x^92 + 117*x^91 + 60*x^90 + 19*x^89 + 114*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 38*x^84 + 73*x^83 + 100*x^82 + 79*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 51*x^75 + 116*x^74 + 37*x^73 + 14*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 10*x^68 + 55*x^67 + 44*x^66 + 81*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 41*x^27 + 108*x^26 + 127*x^25 + 58*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 126*x^20 + 45*x^19 + 52*x^18 + 75*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 23*x^11 + 36*x^10 + 97*x^9 + 118*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 2*x^4 + 107*x^3 + 124*x^2 + 125*x + 54, x^95 + 15*x^93 + 110*x^92 + 37*x^91 + 44*x^90 + 3*x^89 + 74*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 110*x^84 + 89*x^83 + 116*x^82 + 31*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 67*x^75 + 68*x^74 + 117*x^73 + 54*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 2*x^68 + 103*x^67 + 92*x^66 + 65*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 25*x^27 + 28*x^26 + 47*x^25 + 114*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 102*x^20 + 125*x^19 + 4*x^18 + 91*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 103*x^11 + 52*x^10 + 113*x^9 + 126*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 26*x^4 + 91*x^3 + 108*x^2 + 45*x + 62, x^95 + 15*x^93 + 82*x^92 + 85*x^91 + 100*x^90 + 83*x^89 + 38*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 114*x^84 + 105*x^83 + 60*x^82 + 15*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 83*x^75 + 108*x^74 + 101*x^73 + 26*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 94*x^68 + 23*x^67 + 52*x^66 + 17*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 9*x^27 + 52*x^26 + 63*x^25 + 62*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 122*x^20 + 77*x^19 + 108*x^18 + 11*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 55*x^11 + 60*x^10 + 33*x^9 + 18*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 70*x^4 + 75*x^3 + 100*x^2 + 61*x + 114, x^95 + 15*x^93 + 50*x^92 + 37*x^91 + 52*x^90 + 67*x^89 + 54*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 114*x^84 + 89*x^83 + 44*x^82 + 95*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 67*x^75 + 92*x^74 + 53*x^73 + 74*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 30*x^68 + 103*x^67 + 4*x^66 + x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 25*x^27 + 68*x^26 + 111*x^25 + 14*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 122*x^20 + 125*x^19 + 28*x^18 + 27*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 103*x^11 + 108*x^10 + 49*x^9 + 2*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 6*x^4 + 91*x^3 + 116*x^2 + 109*x + 2, x^95 + 15*x^93 + 98*x^92 + 5*x^91 + 116*x^90 + 99*x^89 + 102*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 98*x^84 + 121*x^83 + 108*x^82 + 63*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 99*x^75 + 28*x^74 + 21*x^73 + 26*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 46*x^68 + 71*x^67 + 68*x^66 + 33*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 121*x^27 + 4*x^26 + 15*x^25 + 126*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 42*x^20 + 29*x^19 + 92*x^18 + 123*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 7*x^11 + 44*x^10 + 17*x^9 + 18*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 86*x^4 + 59*x^3 + 52*x^2 + 13*x + 82, x^95 + 15*x^93 + 114*x^92 + 101*x^91 + 52*x^90 + 3*x^89 + 118*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 50*x^84 + 25*x^83 + 44*x^82 + 31*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 3*x^75 + 92*x^74 + 117*x^73 + 10*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 94*x^68 + 39*x^67 + 4*x^66 + 65*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 89*x^27 + 68*x^26 + 47*x^25 + 78*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 58*x^20 + 61*x^19 + 28*x^18 + 91*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 39*x^11 + 108*x^10 + 113*x^9 + 66*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 70*x^4 + 27*x^3 + 116*x^2 + 45*x + 66, x^95 + 15*x^93 + 38*x^92 + 69*x^91 + 76*x^90 + 3*x^89 + 98*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 70*x^84 + 57*x^83 + 20*x^82 + 31*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 35*x^75 + 36*x^74 + 117*x^73 + 94*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 42*x^68 + 7*x^67 + 60*x^66 + 65*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 57*x^27 + 60*x^26 + 47*x^25 + 106*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 30*x^20 + 93*x^19 + 36*x^18 + 91*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 71*x^11 + 20*x^10 + 113*x^9 + 6*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 34*x^4 + 123*x^3 + 76*x^2 + 45*x + 102, x^95 + 15*x^93 + 86*x^92 + 21*x^91 + 60*x^90 + 51*x^89 + 34*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 22*x^84 + 41*x^83 + 100*x^82 + 47*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 19*x^75 + 116*x^74 + 5*x^73 + 94*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 26*x^68 + 87*x^67 + 44*x^66 + 113*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 73*x^27 + 108*x^26 + 31*x^25 + 42*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 46*x^20 + 13*x^19 + 52*x^18 + 43*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 119*x^11 + 36*x^10 + 65*x^9 + 6*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 82*x^4 + 11*x^3 + 124*x^2 + 29*x + 6, x^95 + 15*x^93 + 38*x^92 + 69*x^91 + 12*x^90 + 3*x^89 + 34*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 70*x^84 + 57*x^83 + 84*x^82 + 31*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 35*x^75 + 100*x^74 + 117*x^73 + 30*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 42*x^68 + 7*x^67 + 124*x^66 + 65*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 57*x^27 + 124*x^26 + 47*x^25 + 42*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 30*x^20 + 93*x^19 + 100*x^18 + 91*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 71*x^11 + 84*x^10 + 113*x^9 + 70*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 34*x^4 + 123*x^3 + 12*x^2 + 45*x + 38, x^95 + 15*x^93 + 42*x^92 + 101*x^91 + 116*x^90 + 99*x^89 + 110*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 74*x^84 + 25*x^83 + 44*x^82 + 63*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 3*x^75 + 28*x^74 + 21*x^73 + 82*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 70*x^68 + 39*x^67 + 4*x^66 + 33*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 89*x^27 + 4*x^26 + 15*x^25 + 38*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 50*x^20 + 61*x^19 + 28*x^18 + 123*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 39*x^11 + 44*x^10 + 17*x^9 + 106*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 14*x^4 + 27*x^3 + 116*x^2 + 13*x + 74, x^95 + 15*x^93 + 34*x^92 + 117*x^91 + 68*x^90 + 51*x^89 + 86*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 66*x^84 + 73*x^83 + 92*x^82 + 47*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 51*x^75 + 12*x^74 + 5*x^73 + 106*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 14*x^68 + 55*x^67 + 20*x^66 + 113*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 41*x^27 + 20*x^26 + 31*x^25 + 46*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 10*x^20 + 45*x^19 + 12*x^18 + 43*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 23*x^11 + 92*x^10 + 65*x^9 + 34*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 54*x^4 + 107*x^3 + 68*x^2 + 29*x + 2, x^95 + 15*x^93 + 114*x^92 + 117*x^91 + 68*x^90 + 51*x^89 + 102*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 82*x^84 + 73*x^83 + 92*x^82 + 47*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 51*x^75 + 12*x^74 + 5*x^73 + 90*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 126*x^68 + 55*x^67 + 20*x^66 + 113*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 41*x^27 + 20*x^26 + 31*x^25 + 126*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 90*x^20 + 45*x^19 + 12*x^18 + 43*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 23*x^11 + 92*x^10 + 65*x^9 + 82*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 102*x^4 + 107*x^3 + 68*x^2 + 29*x + 114, x^95 + 15*x^93 + 106*x^92 + 85*x^91 + 100*x^90 + 115*x^89 + 126*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 106*x^84 + 105*x^83 + 124*x^82 + 111*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 83*x^75 + 108*x^74 + 69*x^73 + 2*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 102*x^68 + 23*x^67 + 116*x^66 + 49*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 9*x^27 + 52*x^26 + 95*x^25 + 118*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 82*x^20 + 77*x^19 + 44*x^18 + 107*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 55*x^11 + 60*x^10 + x^9 + 90*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 46*x^4 + 75*x^3 + 36*x^2 + 93*x + 26, x^95 + 15*x^93 + 66*x^92 + 117*x^91 + 100*x^90 + 51*x^89 + 86*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 34*x^84 + 73*x^83 + 60*x^82 + 47*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 51*x^75 + 108*x^74 + 5*x^73 + 106*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 46*x^68 + 55*x^67 + 52*x^66 + 113*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 41*x^27 + 52*x^26 + 31*x^25 + 46*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 106*x^20 + 45*x^19 + 108*x^18 + 43*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 23*x^11 + 60*x^10 + 65*x^9 + 34*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 86*x^4 + 107*x^3 + 100*x^2 + 29*x + 66, x^95 + 15*x^93 + 10*x^92 + 117*x^91 + 100*x^90 + 19*x^89 + 94*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 10*x^84 + 73*x^83 + 124*x^82 + 79*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 51*x^75 + 108*x^74 + 37*x^73 + 34*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 70*x^68 + 55*x^67 + 116*x^66 + 81*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 41*x^27 + 52*x^26 + 127*x^25 + 86*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 114*x^20 + 45*x^19 + 44*x^18 + 75*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 23*x^11 + 60*x^10 + 97*x^9 + 122*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 14*x^4 + 107*x^3 + 36*x^2 + 125*x + 58, x^95 + 15*x^93 + 22*x^92 + 69*x^91 + 76*x^90 + 67*x^89 + 82*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 118*x^84 + 57*x^83 + 20*x^82 + 95*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 35*x^75 + 36*x^74 + 53*x^73 + 110*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 122*x^68 + 7*x^67 + 60*x^66 + x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 57*x^27 + 60*x^26 + 111*x^25 + 26*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 14*x^20 + 93*x^19 + 36*x^18 + 27*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 71*x^11 + 20*x^10 + 49*x^9 + 86*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 50*x^4 + 123*x^3 + 76*x^2 + 109*x + 118, x^95 + 15*x^93 + 86*x^92 + 21*x^91 + 28*x^90 + 115*x^89 + 2*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 86*x^84 + 41*x^83 + 4*x^82 + 111*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 19*x^75 + 20*x^74 + 69*x^73 + 126*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 90*x^68 + 87*x^67 + 12*x^66 + 49*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 73*x^27 + 76*x^26 + 95*x^25 + 10*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 110*x^20 + 13*x^19 + 84*x^18 + 107*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 119*x^11 + 68*x^10 + x^9 + 38*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 18*x^4 + 11*x^3 + 92*x^2 + 93*x + 102, x^95 + 15*x^93 + 2*x^92 + 21*x^91 + 36*x^90 + 19*x^89 + 86*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 98*x^84 + 41*x^83 + 124*x^82 + 79*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 19*x^75 + 44*x^74 + 37*x^73 + 106*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 110*x^68 + 87*x^67 + 116*x^66 + 81*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 73*x^27 + 116*x^26 + 127*x^25 + 46*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 42*x^20 + 13*x^19 + 44*x^18 + 75*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 119*x^11 + 124*x^10 + 97*x^9 + 34*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 22*x^4 + 11*x^3 + 36*x^2 + 125*x + 66, x^95 + 15*x^93 + 6*x^92 + 53*x^91 + 28*x^90 + 19*x^89 + 50*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 70*x^84 + 9*x^83 + 4*x^82 + 79*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 115*x^75 + 20*x^74 + 37*x^73 + 78*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 106*x^68 + 119*x^67 + 12*x^66 + 81*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 105*x^27 + 76*x^26 + 127*x^25 + 122*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 30*x^20 + 109*x^19 + 84*x^18 + 75*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 87*x^11 + 68*x^10 + 97*x^9 + 54*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 98*x^4 + 43*x^3 + 92*x^2 + 125*x + 54, x^95 + 15*x^93 + 34*x^92 + 117*x^91 + 36*x^90 + 115*x^89 + 54*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 2*x^84 + 73*x^83 + 124*x^82 + 111*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 51*x^75 + 44*x^74 + 69*x^73 + 10*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 78*x^68 + 55*x^67 + 116*x^66 + 49*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 41*x^27 + 116*x^26 + 95*x^25 + 14*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 74*x^20 + 45*x^19 + 44*x^18 + 107*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 23*x^11 + 124*x^10 + x^9 + 66*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 118*x^4 + 107*x^3 + 36*x^2 + 93*x + 98, x^95 + 15*x^93 + 62*x^92 + 53*x^91 + 92*x^90 + 51*x^89 + 42*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 94*x^84 + 9*x^83 + 4*x^82 + 47*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 115*x^75 + 84*x^74 + 5*x^73 + 22*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 82*x^68 + 119*x^67 + 12*x^66 + 113*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 105*x^27 + 12*x^26 + 31*x^25 + 82*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 22*x^20 + 109*x^19 + 84*x^18 + 43*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 87*x^11 + 4*x^10 + 65*x^9 + 94*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 42*x^4 + 43*x^3 + 92*x^2 + 29*x + 62, x^95 + 15*x^93 + 110*x^92 + 85*x^91 + 92*x^90 + 19*x^89 + 26*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 78*x^84 + 105*x^83 + 4*x^82 + 79*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 83*x^75 + 84*x^74 + 37*x^73 + 38*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 98*x^68 + 23*x^67 + 12*x^66 + 81*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 9*x^27 + 12*x^26 + 127*x^25 + 2*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 70*x^20 + 77*x^19 + 84*x^18 + 75*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 55*x^11 + 4*x^10 + 97*x^9 + 46*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 122*x^4 + 75*x^3 + 92*x^2 + 125*x + 78, x^95 + 15*x^93 + 2*x^92 + 53*x^91 + 4*x^90 + 115*x^89 + 118*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 34*x^84 + 9*x^83 + 28*x^82 + 111*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 115*x^75 + 76*x^74 + 69*x^73 + 74*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 46*x^68 + 119*x^67 + 84*x^66 + 49*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 105*x^27 + 84*x^26 + 95*x^25 + 78*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 106*x^20 + 109*x^19 + 76*x^18 + 107*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 87*x^11 + 28*x^10 + x^9 + 2*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 86*x^4 + 43*x^3 + 4*x^2 + 93*x + 98, x^95 + 15*x^93 + 26*x^92 + 53*x^91 + 68*x^90 + 19*x^89 + 14*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 26*x^84 + 9*x^83 + 28*x^82 + 79*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 115*x^75 + 12*x^74 + 37*x^73 + 114*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 54*x^68 + 119*x^67 + 84*x^66 + 81*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 105*x^27 + 20*x^26 + 127*x^25 + 70*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 66*x^20 + 109*x^19 + 76*x^18 + 75*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 87*x^11 + 92*x^10 + 97*x^9 + 10*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 62*x^4 + 43*x^3 + 4*x^2 + 125*x + 74, x^95 + 15*x^93 + 6*x^92 + 21*x^91 + 124*x^90 + 51*x^89 + 82*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 6*x^84 + 41*x^83 + 36*x^82 + 47*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 19*x^75 + 52*x^74 + 5*x^73 + 46*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 42*x^68 + 87*x^67 + 108*x^66 + 113*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 73*x^27 + 44*x^26 + 31*x^25 + 26*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 94*x^20 + 13*x^19 + 116*x^18 + 43*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 119*x^11 + 100*x^10 + 65*x^9 + 22*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 34*x^4 + 11*x^3 + 60*x^2 + 29*x + 86, x^95 + 15*x^93 + 90*x^92 + 53*x^91 + 4*x^90 + 83*x^89 + 78*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 90*x^84 + 9*x^83 + 92*x^82 + 15*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 115*x^75 + 76*x^74 + 101*x^73 + 50*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 118*x^68 + 119*x^67 + 20*x^66 + 17*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 105*x^27 + 84*x^26 + 63*x^25 + 6*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 2*x^20 + 109*x^19 + 12*x^18 + 11*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 87*x^11 + 28*x^10 + 33*x^9 + 74*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 126*x^4 + 43*x^3 + 68*x^2 + 61*x + 10, x^95 + 15*x^93 + 98*x^92 + 117*x^91 + 68*x^90 + 115*x^89 + 86*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 2*x^84 + 73*x^83 + 92*x^82 + 111*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 51*x^75 + 12*x^74 + 69*x^73 + 106*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 78*x^68 + 55*x^67 + 20*x^66 + 49*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 41*x^27 + 20*x^26 + 95*x^25 + 46*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 74*x^20 + 45*x^19 + 12*x^18 + 107*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 23*x^11 + 92*x^10 + x^9 + 34*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 118*x^4 + 107*x^3 + 68*x^2 + 93*x + 2, x^95 + 15*x^93 + 118*x^92 + 101*x^91 + 76*x^90 + 35*x^89 + 50*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 86*x^84 + 25*x^83 + 20*x^82 + 127*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 3*x^75 + 36*x^74 + 85*x^73 + 14*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 26*x^68 + 39*x^67 + 60*x^66 + 97*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 89*x^27 + 60*x^26 + 79*x^25 + 122*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 110*x^20 + 61*x^19 + 36*x^18 + 59*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 39*x^11 + 20*x^10 + 81*x^9 + 118*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 82*x^4 + 27*x^3 + 76*x^2 + 77*x + 22, x^95 + 15*x^93 + 78*x^92 + 101*x^91 + 12*x^90 + 3*x^89 + 10*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 14*x^84 + 25*x^83 + 20*x^82 + 31*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 3*x^75 + 100*x^74 + 117*x^73 + 118*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 98*x^68 + 39*x^67 + 60*x^66 + 65*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 89*x^27 + 124*x^26 + 47*x^25 + 50*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 6*x^20 + 61*x^19 + 36*x^18 + 91*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 39*x^11 + 84*x^10 + 113*x^9 + 62*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 122*x^4 + 27*x^3 + 76*x^2 + 45*x + 62, x^95 + 15*x^93 + 30*x^92 + 85*x^91 + 28*x^90 + 83*x^89 + 10*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 62*x^84 + 105*x^83 + 68*x^82 + 15*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 83*x^75 + 20*x^74 + 101*x^73 + 54*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 114*x^68 + 23*x^67 + 76*x^66 + 17*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 9*x^27 + 76*x^26 + 63*x^25 + 50*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 118*x^20 + 77*x^19 + 20*x^18 + 11*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 55*x^11 + 68*x^10 + 33*x^9 + 126*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 74*x^4 + 75*x^3 + 28*x^2 + 61*x + 94, x^95 + 15*x^93 + 102*x^92 + 69*x^91 + 108*x^90 + 3*x^89 + 2*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 70*x^84 + 57*x^83 + 116*x^82 + 31*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 35*x^75 + 4*x^74 + 117*x^73 + 62*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 42*x^68 + 7*x^67 + 92*x^66 + 65*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 57*x^27 + 92*x^26 + 47*x^25 + 10*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 30*x^20 + 93*x^19 + 4*x^18 + 91*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 71*x^11 + 116*x^10 + 113*x^9 + 102*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 34*x^4 + 123*x^3 + 108*x^2 + 45*x + 6, x^95 + 15*x^93 + 66*x^92 + 5*x^91 + 116*x^90 + 35*x^89 + 6*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 66*x^84 + 121*x^83 + 108*x^82 + 127*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 99*x^75 + 28*x^74 + 85*x^73 + 122*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 78*x^68 + 71*x^67 + 68*x^66 + 97*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 121*x^27 + 4*x^26 + 79*x^25 + 30*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 10*x^20 + 29*x^19 + 92*x^18 + 59*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 7*x^11 + 44*x^10 + 81*x^9 + 114*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 118*x^4 + 59*x^3 + 52*x^2 + 77*x + 50, x^95 + 15*x^93 + 54*x^92 + 69*x^91 + 108*x^90 + 3*x^89 + 18*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 86*x^84 + 57*x^83 + 116*x^82 + 31*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 35*x^75 + 4*x^74 + 117*x^73 + 46*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 26*x^68 + 7*x^67 + 92*x^66 + 65*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 57*x^27 + 92*x^26 + 47*x^25 + 90*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 110*x^20 + 93*x^19 + 4*x^18 + 91*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 71*x^11 + 116*x^10 + 113*x^9 + 22*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 82*x^4 + 123*x^3 + 108*x^2 + 45*x + 118, x^95 + 15*x^93 + 62*x^92 + 101*x^91 + 76*x^90 + 3*x^89 + 122*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 62*x^84 + 25*x^83 + 84*x^82 + 31*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 3*x^75 + 36*x^74 + 117*x^73 + 6*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 50*x^68 + 39*x^67 + 124*x^66 + 65*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 89*x^27 + 60*x^26 + 47*x^25 + 98*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 118*x^20 + 61*x^19 + 100*x^18 + 91*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 39*x^11 + 20*x^10 + 113*x^9 + 14*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 10*x^4 + 27*x^3 + 12*x^2 + 45*x + 78, x^95 + 15*x^93 + 6*x^92 + 69*x^91 + 76*x^90 + 67*x^89 + 2*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 38*x^84 + 57*x^83 + 20*x^82 + 95*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 35*x^75 + 36*x^74 + 53*x^73 + 62*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 74*x^68 + 7*x^67 + 60*x^66 + x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 57*x^27 + 60*x^26 + 111*x^25 + 10*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 126*x^20 + 93*x^19 + 36*x^18 + 27*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 71*x^11 + 20*x^10 + 49*x^9 + 102*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 66*x^4 + 123*x^3 + 76*x^2 + 109*x + 70, x^95 + 15*x^93 + 34*x^92 + 117*x^91 + 100*x^90 + 51*x^89 + 54*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 2*x^84 + 73*x^83 + 60*x^82 + 47*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 51*x^75 + 108*x^74 + 5*x^73 + 10*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 78*x^68 + 55*x^67 + 52*x^66 + 113*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 41*x^27 + 52*x^26 + 31*x^25 + 14*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 74*x^20 + 45*x^19 + 108*x^18 + 43*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 23*x^11 + 60*x^10 + 65*x^9 + 66*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 118*x^4 + 107*x^3 + 100*x^2 + 29*x + 98, x^95 + 15*x^93 + 34*x^92 + 85*x^91 + 36*x^90 + 83*x^89 + 118*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 2*x^84 + 105*x^83 + 124*x^82 + 15*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 83*x^75 + 44*x^74 + 101*x^73 + 74*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 78*x^68 + 23*x^67 + 116*x^66 + 17*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 9*x^27 + 116*x^26 + 63*x^25 + 78*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 74*x^20 + 77*x^19 + 44*x^18 + 11*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 55*x^11 + 124*x^10 + 33*x^9 + 2*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 118*x^4 + 75*x^3 + 36*x^2 + 61*x + 34, x^95 + 15*x^93 + 122*x^92 + 5*x^91 + 116*x^90 + 3*x^89 + 62*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 90*x^84 + 121*x^83 + 44*x^82 + 31*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 99*x^75 + 28*x^74 + 117*x^73 + 2*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 54*x^68 + 71*x^67 + 4*x^66 + 65*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 121*x^27 + 4*x^26 + 47*x^25 + 54*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 2*x^20 + 29*x^19 + 28*x^18 + 91*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 7*x^11 + 44*x^10 + 113*x^9 + 90*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 62*x^4 + 59*x^3 + 116*x^2 + 45*x + 122, x^95 + 15*x^93 + 70*x^92 + 21*x^91 + 92*x^90 + 51*x^89 + 50*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 6*x^84 + 41*x^83 + 68*x^82 + 47*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 19*x^75 + 84*x^74 + 5*x^73 + 78*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 42*x^68 + 87*x^67 + 76*x^66 + 113*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 73*x^27 + 12*x^26 + 31*x^25 + 122*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 94*x^20 + 13*x^19 + 20*x^18 + 43*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 119*x^11 + 4*x^10 + 65*x^9 + 54*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 34*x^4 + 11*x^3 + 28*x^2 + 29*x + 54, x^95 + 15*x^93 + 98*x^92 + 117*x^91 + 68*x^90 + 51*x^89 + 22*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 2*x^84 + 73*x^83 + 92*x^82 + 47*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 51*x^75 + 12*x^74 + 5*x^73 + 42*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 78*x^68 + 55*x^67 + 20*x^66 + 113*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 41*x^27 + 20*x^26 + 31*x^25 + 110*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 74*x^20 + 45*x^19 + 12*x^18 + 43*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 23*x^11 + 92*x^10 + 65*x^9 + 98*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 118*x^4 + 107*x^3 + 68*x^2 + 29*x + 66, x^95 + 15*x^93 + 82*x^92 + 117*x^91 + 68*x^90 + 115*x^89 + 6*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 50*x^84 + 73*x^83 + 92*x^82 + 111*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 51*x^75 + 12*x^74 + 69*x^73 + 58*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 30*x^68 + 55*x^67 + 20*x^66 + 49*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 41*x^27 + 20*x^26 + 95*x^25 + 30*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 58*x^20 + 45*x^19 + 12*x^18 + 107*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 23*x^11 + 92*x^10 + x^9 + 50*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 6*x^4 + 107*x^3 + 68*x^2 + 93*x + 82, x^95 + 15*x^93 + 26*x^92 + 21*x^91 + 36*x^90 + 115*x^89 + 110*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 90*x^84 + 41*x^83 + 60*x^82 + 111*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 19*x^75 + 44*x^74 + 69*x^73 + 18*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 118*x^68 + 87*x^67 + 52*x^66 + 49*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 73*x^27 + 116*x^26 + 95*x^25 + 38*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 2*x^20 + 13*x^19 + 108*x^18 + 107*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 119*x^11 + 124*x^10 + x^9 + 42*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 126*x^4 + 11*x^3 + 100*x^2 + 93*x + 42, x^95 + 15*x^93 + 2*x^92 + 101*x^91 + 52*x^90 + 3*x^89 + 70*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 2*x^84 + 25*x^83 + 44*x^82 + 31*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 3*x^75 + 92*x^74 + 117*x^73 + 58*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 14*x^68 + 39*x^67 + 4*x^66 + 65*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 89*x^27 + 68*x^26 + 47*x^25 + 94*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 74*x^20 + 61*x^19 + 28*x^18 + 91*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 39*x^11 + 108*x^10 + 113*x^9 + 50*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 54*x^4 + 27*x^3 + 116*x^2 + 45*x + 114, x^95 + 15*x^93 + 106*x^92 + 117*x^91 + 36*x^90 + 83*x^89 + 62*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 106*x^84 + 73*x^83 + 60*x^82 + 15*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 51*x^75 + 44*x^74 + 101*x^73 + 66*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 102*x^68 + 55*x^67 + 52*x^66 + 17*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 41*x^27 + 116*x^26 + 63*x^25 + 54*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 82*x^20 + 45*x^19 + 108*x^18 + 11*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 23*x^11 + 124*x^10 + 33*x^9 + 26*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 46*x^4 + 107*x^3 + 100*x^2 + 61*x + 90, x^95 + 15*x^93 + 42*x^92 + 53*x^91 + 68*x^90 + 19*x^89 + 94*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 106*x^84 + 9*x^83 + 28*x^82 + 79*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 115*x^75 + 12*x^74 + 37*x^73 + 34*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 102*x^68 + 119*x^67 + 84*x^66 + 81*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 105*x^27 + 20*x^26 + 127*x^25 + 86*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 82*x^20 + 109*x^19 + 76*x^18 + 75*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 87*x^11 + 92*x^10 + 97*x^9 + 122*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 46*x^4 + 43*x^3 + 4*x^2 + 125*x + 122, x^95 + 15*x^93 + 82*x^92 + 53*x^91 + 36*x^90 + 51*x^89 + 38*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 114*x^84 + 9*x^83 + 124*x^82 + 47*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 115*x^75 + 44*x^74 + 5*x^73 + 26*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 94*x^68 + 119*x^67 + 116*x^66 + 113*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 105*x^27 + 116*x^26 + 31*x^25 + 62*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 122*x^20 + 109*x^19 + 44*x^18 + 43*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 87*x^11 + 124*x^10 + 65*x^9 + 18*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 70*x^4 + 43*x^3 + 36*x^2 + 29*x + 114, x^95 + 15*x^93 + 26*x^92 + 69*x^91 + 52*x^90 + 67*x^89 + 30*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 122*x^84 + 57*x^83 + 108*x^82 + 95*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 35*x^75 + 92*x^74 + 53*x^73 + 34*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 22*x^68 + 7*x^67 + 68*x^66 + x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 57*x^27 + 68*x^26 + 111*x^25 + 22*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 34*x^20 + 93*x^19 + 92*x^18 + 27*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 71*x^11 + 108*x^10 + 49*x^9 + 122*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 30*x^4 + 123*x^3 + 52*x^2 + 109*x + 26, x^95 + 15*x^93 + 122*x^92 + 5*x^91 + 116*x^90 + 67*x^89 + 126*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 90*x^84 + 121*x^83 + 44*x^82 + 95*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 99*x^75 + 28*x^74 + 53*x^73 + 66*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 54*x^68 + 71*x^67 + 4*x^66 + x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 121*x^27 + 4*x^26 + 111*x^25 + 118*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 2*x^20 + 29*x^19 + 28*x^18 + 27*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 7*x^11 + 44*x^10 + 49*x^9 + 26*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 62*x^4 + 59*x^3 + 116*x^2 + 109*x + 58, x^95 + 15*x^93 + 126*x^92 + 53*x^91 + 92*x^90 + 51*x^89 + 106*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 30*x^84 + 9*x^83 + 4*x^82 + 47*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 115*x^75 + 84*x^74 + 5*x^73 + 86*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 18*x^68 + 119*x^67 + 12*x^66 + 113*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 105*x^27 + 12*x^26 + 31*x^25 + 18*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 86*x^20 + 109*x^19 + 84*x^18 + 43*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 87*x^11 + 4*x^10 + 65*x^9 + 30*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 106*x^4 + 43*x^3 + 92*x^2 + 29*x + 126, x^95 + 15*x^93 + 110*x^92 + 101*x^91 + 76*x^90 + 67*x^89 + 42*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 46*x^84 + 25*x^83 + 84*x^82 + 95*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 3*x^75 + 36*x^74 + 53*x^73 + 86*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 66*x^68 + 39*x^67 + 124*x^66 + x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 89*x^27 + 60*x^26 + 111*x^25 + 82*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 38*x^20 + 61*x^19 + 100*x^18 + 27*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 39*x^11 + 20*x^10 + 49*x^9 + 30*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 90*x^4 + 27*x^3 + 12*x^2 + 109*x + 30, x^95 + 15*x^93 + 18*x^92 + 69*x^91 + 116*x^90 + 35*x^89 + 86*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 82*x^84 + 57*x^83 + 108*x^82 + 127*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 35*x^75 + 28*x^74 + 85*x^73 + 42*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 62*x^68 + 7*x^67 + 68*x^66 + 97*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 57*x^27 + 4*x^26 + 79*x^25 + 46*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 90*x^20 + 93*x^19 + 92*x^18 + 59*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 71*x^11 + 44*x^10 + 81*x^9 + 98*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 38*x^4 + 123*x^3 + 52*x^2 + 77*x + 98, x^95 + 15*x^93 + 34*x^92 + 117*x^91 + 68*x^90 + 115*x^89 + 22*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 66*x^84 + 73*x^83 + 92*x^82 + 111*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 51*x^75 + 12*x^74 + 69*x^73 + 42*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 14*x^68 + 55*x^67 + 20*x^66 + 49*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 41*x^27 + 20*x^26 + 95*x^25 + 110*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 10*x^20 + 45*x^19 + 12*x^18 + 107*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 23*x^11 + 92*x^10 + x^9 + 98*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 54*x^4 + 107*x^3 + 68*x^2 + 93*x + 66, x^95 + 15*x^93 + 2*x^92 + 37*x^91 + 116*x^90 + 3*x^89 + 70*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 2*x^84 + 89*x^83 + 108*x^82 + 31*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 67*x^75 + 28*x^74 + 117*x^73 + 58*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 14*x^68 + 103*x^67 + 68*x^66 + 65*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 25*x^27 + 4*x^26 + 47*x^25 + 94*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 74*x^20 + 125*x^19 + 92*x^18 + 91*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 103*x^11 + 44*x^10 + 113*x^9 + 50*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 54*x^4 + 91*x^3 + 52*x^2 + 45*x + 114, x^95 + 15*x^93 + 34*x^92 + 21*x^91 + 36*x^90 + 19*x^89 + 118*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 2*x^84 + 41*x^83 + 124*x^82 + 79*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 19*x^75 + 44*x^74 + 37*x^73 + 74*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 78*x^68 + 87*x^67 + 116*x^66 + 81*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 73*x^27 + 116*x^26 + 127*x^25 + 78*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 74*x^20 + 13*x^19 + 44*x^18 + 75*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 119*x^11 + 124*x^10 + 97*x^9 + 2*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 118*x^4 + 11*x^3 + 36*x^2 + 125*x + 34, x^95 + 15*x^93 + 122*x^92 + 53*x^91 + 100*x^90 + 83*x^89 + 14*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 58*x^84 + 9*x^83 + 124*x^82 + 15*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 115*x^75 + 108*x^74 + 101*x^73 + 114*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 22*x^68 + 119*x^67 + 116*x^66 + 17*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 105*x^27 + 52*x^26 + 63*x^25 + 70*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 98*x^20 + 109*x^19 + 44*x^18 + 11*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 87*x^11 + 60*x^10 + 33*x^9 + 10*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 30*x^4 + 43*x^3 + 36*x^2 + 61*x + 10, x^95 + 15*x^93 + 22*x^92 + 21*x^91 + 92*x^90 + 115*x^89 + 2*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 22*x^84 + 41*x^83 + 68*x^82 + 111*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 19*x^75 + 84*x^74 + 69*x^73 + 126*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 26*x^68 + 87*x^67 + 76*x^66 + 49*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 73*x^27 + 12*x^26 + 95*x^25 + 10*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 46*x^20 + 13*x^19 + 20*x^18 + 107*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 119*x^11 + 4*x^10 + x^9 + 38*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 82*x^4 + 11*x^3 + 28*x^2 + 93*x + 102, x^95 + 15*x^93 + 98*x^92 + 53*x^91 + 4*x^90 + 115*x^89 + 86*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 2*x^84 + 9*x^83 + 28*x^82 + 111*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 115*x^75 + 76*x^74 + 69*x^73 + 106*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 78*x^68 + 119*x^67 + 84*x^66 + 49*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 105*x^27 + 84*x^26 + 95*x^25 + 46*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 74*x^20 + 109*x^19 + 76*x^18 + 107*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 87*x^11 + 28*x^10 + x^9 + 34*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 118*x^4 + 43*x^3 + 4*x^2 + 93*x + 2, x^95 + 15*x^93 + 50*x^92 + 117*x^91 + 36*x^90 + 51*x^89 + 70*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 82*x^84 + 73*x^83 + 124*x^82 + 47*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 51*x^75 + 44*x^74 + 5*x^73 + 122*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 126*x^68 + 55*x^67 + 116*x^66 + 113*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 41*x^27 + 116*x^26 + 31*x^25 + 94*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 90*x^20 + 45*x^19 + 44*x^18 + 43*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 23*x^11 + 124*x^10 + 65*x^9 + 114*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 102*x^4 + 107*x^3 + 36*x^2 + 29*x + 82, x^95 + 15*x^93 + 78*x^92 + 21*x^91 + 28*x^90 + 19*x^89 + 122*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 46*x^84 + 41*x^83 + 68*x^82 + 79*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 19*x^75 + 20*x^74 + 37*x^73 + 70*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 2*x^68 + 87*x^67 + 76*x^66 + 81*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 73*x^27 + 76*x^26 + 127*x^25 + 98*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 38*x^20 + 13*x^19 + 20*x^18 + 75*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 119*x^11 + 68*x^10 + 97*x^9 + 78*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 26*x^4 + 11*x^3 + 28*x^2 + 125*x + 110, x^95 + 15*x^93 + 38*x^92 + 117*x^91 + 28*x^90 + 83*x^89 + 82*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 102*x^84 + 73*x^83 + 4*x^82 + 15*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 51*x^75 + 20*x^74 + 101*x^73 + 46*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 74*x^68 + 55*x^67 + 12*x^66 + 17*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 41*x^27 + 76*x^26 + 63*x^25 + 26*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 62*x^20 + 45*x^19 + 84*x^18 + 11*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 23*x^11 + 68*x^10 + 33*x^9 + 22*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 66*x^4 + 107*x^3 + 92*x^2 + 61*x + 22, x^95 + 15*x^93 + 90*x^92 + 117*x^91 + 36*x^90 + 19*x^89 + 46*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 26*x^84 + 73*x^83 + 60*x^82 + 79*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 51*x^75 + 44*x^74 + 37*x^73 + 82*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 54*x^68 + 55*x^67 + 52*x^66 + 81*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 41*x^27 + 116*x^26 + 127*x^25 + 102*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 66*x^20 + 45*x^19 + 108*x^18 + 75*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 23*x^11 + 124*x^10 + 97*x^9 + 106*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 62*x^4 + 107*x^3 + 100*x^2 + 125*x + 106, x^95 + 15*x^93 + 38*x^92 + 37*x^91 + 44*x^90 + 99*x^89 + 66*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 6*x^84 + 89*x^83 + 52*x^82 + 63*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 67*x^75 + 68*x^74 + 21*x^73 + 126*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 106*x^68 + 103*x^67 + 28*x^66 + 33*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 25*x^27 + 28*x^26 + 15*x^25 + 74*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 94*x^20 + 125*x^19 + 68*x^18 + 123*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 103*x^11 + 52*x^10 + 17*x^9 + 38*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 98*x^4 + 91*x^3 + 44*x^2 + 13*x + 70, x^95 + 15*x^93 + 46*x^92 + 101*x^91 + 44*x^90 + 3*x^89 + 74*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 46*x^84 + 25*x^83 + 116*x^82 + 31*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 3*x^75 + 68*x^74 + 117*x^73 + 54*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 66*x^68 + 39*x^67 + 92*x^66 + 65*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 89*x^27 + 28*x^26 + 47*x^25 + 114*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 38*x^20 + 61*x^19 + 4*x^18 + 91*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 39*x^11 + 52*x^10 + 113*x^9 + 126*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 90*x^4 + 27*x^3 + 108*x^2 + 45*x + 62, x^95 + 15*x^93 + 122*x^92 + 69*x^91 + 116*x^90 + 67*x^89 + 62*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 90*x^84 + 57*x^83 + 44*x^82 + 95*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 35*x^75 + 28*x^74 + 53*x^73 + 2*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 54*x^68 + 7*x^67 + 4*x^66 + x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 57*x^27 + 4*x^26 + 111*x^25 + 54*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 2*x^20 + 93*x^19 + 28*x^18 + 27*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 71*x^11 + 44*x^10 + 49*x^9 + 90*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 62*x^4 + 123*x^3 + 116*x^2 + 109*x + 122, x^95 + 15*x^93 + 18*x^92 + 37*x^91 + 84*x^90 + 67*x^89 + 118*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 18*x^84 + 89*x^83 + 12*x^82 + 95*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 67*x^75 + 60*x^74 + 53*x^73 + 10*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 126*x^68 + 103*x^67 + 36*x^66 + x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 25*x^27 + 100*x^26 + 111*x^25 + 78*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 26*x^20 + 125*x^19 + 124*x^18 + 27*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 103*x^11 + 76*x^10 + 49*x^9 + 66*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 102*x^4 + 91*x^3 + 20*x^2 + 109*x + 2, x^95 + 15*x^93 + 70*x^92 + 5*x^91 + 76*x^90 + 67*x^89 + 2*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 102*x^84 + 121*x^83 + 20*x^82 + 95*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 99*x^75 + 36*x^74 + 53*x^73 + 62*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 10*x^68 + 71*x^67 + 60*x^66 + x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 121*x^27 + 60*x^26 + 111*x^25 + 10*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 62*x^20 + 29*x^19 + 36*x^18 + 27*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 7*x^11 + 20*x^10 + 49*x^9 + 102*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 2*x^4 + 59*x^3 + 76*x^2 + 109*x + 70, x^95 + 15*x^93 + 82*x^92 + 37*x^91 + 52*x^90 + 67*x^89 + 86*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 18*x^84 + 89*x^83 + 44*x^82 + 95*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 67*x^75 + 92*x^74 + 53*x^73 + 42*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 126*x^68 + 103*x^67 + 4*x^66 + x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 25*x^27 + 68*x^26 + 111*x^25 + 46*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 26*x^20 + 125*x^19 + 28*x^18 + 27*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 103*x^11 + 108*x^10 + 49*x^9 + 98*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 102*x^4 + 91*x^3 + 116*x^2 + 109*x + 98, x^95 + 15*x^93 + 102*x^92 + 117*x^91 + 124*x^90 + 19*x^89 + 114*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 102*x^84 + 73*x^83 + 36*x^82 + 79*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 51*x^75 + 52*x^74 + 37*x^73 + 14*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 74*x^68 + 55*x^67 + 108*x^66 + 81*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 41*x^27 + 44*x^26 + 127*x^25 + 58*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 62*x^20 + 45*x^19 + 116*x^18 + 75*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 23*x^11 + 100*x^10 + 97*x^9 + 118*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 66*x^4 + 107*x^3 + 60*x^2 + 125*x + 54, x^95 + 15*x^93 + 102*x^92 + 53*x^91 + 124*x^90 + 83*x^89 + 114*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 102*x^84 + 9*x^83 + 36*x^82 + 15*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 115*x^75 + 52*x^74 + 101*x^73 + 14*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 74*x^68 + 119*x^67 + 108*x^66 + 17*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 105*x^27 + 44*x^26 + 63*x^25 + 58*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 62*x^20 + 109*x^19 + 116*x^18 + 11*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 87*x^11 + 100*x^10 + 33*x^9 + 118*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 66*x^4 + 43*x^3 + 60*x^2 + 61*x + 54, x^95 + 15*x^93 + 26*x^92 + 69*x^91 + 20*x^90 + 67*x^89 + 62*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 58*x^84 + 57*x^83 + 12*x^82 + 95*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 35*x^75 + 124*x^74 + 53*x^73 + 2*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 86*x^68 + 7*x^67 + 36*x^66 + x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 57*x^27 + 36*x^26 + 111*x^25 + 54*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 98*x^20 + 93*x^19 + 124*x^18 + 27*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 71*x^11 + 12*x^10 + 49*x^9 + 90*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 94*x^4 + 123*x^3 + 20*x^2 + 109*x + 58, x^95 + 15*x^93 + 22*x^92 + 37*x^91 + 12*x^90 + 99*x^89 + 18*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 118*x^84 + 89*x^83 + 84*x^82 + 63*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 67*x^75 + 100*x^74 + 21*x^73 + 46*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 122*x^68 + 103*x^67 + 124*x^66 + 33*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 25*x^27 + 124*x^26 + 15*x^25 + 90*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 14*x^20 + 125*x^19 + 100*x^18 + 123*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 103*x^11 + 84*x^10 + 17*x^9 + 22*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 50*x^4 + 91*x^3 + 12*x^2 + 13*x + 54, x^95 + 15*x^93 + 42*x^92 + 21*x^91 + 4*x^90 + 51*x^89 + 30*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 106*x^84 + 41*x^83 + 92*x^82 + 47*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 19*x^75 + 76*x^74 + 5*x^73 + 98*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 102*x^68 + 87*x^67 + 20*x^66 + 113*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 73*x^27 + 84*x^26 + 31*x^25 + 22*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 82*x^20 + 13*x^19 + 12*x^18 + 43*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 119*x^11 + 28*x^10 + 65*x^9 + 58*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 46*x^4 + 11*x^3 + 68*x^2 + 29*x + 58, x^95 + 15*x^93 + 82*x^92 + 85*x^91 + 100*x^90 + 19*x^89 + 102*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 114*x^84 + 105*x^83 + 60*x^82 + 79*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 83*x^75 + 108*x^74 + 37*x^73 + 90*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 94*x^68 + 23*x^67 + 52*x^66 + 81*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 9*x^27 + 52*x^26 + 127*x^25 + 126*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 122*x^20 + 77*x^19 + 108*x^18 + 75*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 55*x^11 + 60*x^10 + 97*x^9 + 82*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 70*x^4 + 75*x^3 + 100*x^2 + 125*x + 50, x^95 + 15*x^93 + 78*x^92 + 21*x^91 + 124*x^90 + 83*x^89 + 90*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 110*x^84 + 41*x^83 + 100*x^82 + 15*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 19*x^75 + 52*x^74 + 101*x^73 + 102*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 66*x^68 + 87*x^67 + 44*x^66 + 17*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 73*x^27 + 44*x^26 + 63*x^25 + 66*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 102*x^20 + 13*x^19 + 52*x^18 + 11*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 119*x^11 + 100*x^10 + 33*x^9 + 110*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 90*x^4 + 11*x^3 + 124*x^2 + 61*x + 78, x^95 + 15*x^93 + 90*x^92 + 85*x^91 + 36*x^90 + 51*x^89 + 46*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 26*x^84 + 105*x^83 + 60*x^82 + 47*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 83*x^75 + 44*x^74 + 5*x^73 + 82*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 54*x^68 + 23*x^67 + 52*x^66 + 113*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 9*x^27 + 116*x^26 + 31*x^25 + 102*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 66*x^20 + 77*x^19 + 108*x^18 + 43*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 55*x^11 + 124*x^10 + 65*x^9 + 106*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 62*x^4 + 75*x^3 + 100*x^2 + 29*x + 106, x^95 + 15*x^93 + 46*x^92 + 5*x^91 + 76*x^90 + 99*x^89 + 42*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 110*x^84 + 121*x^83 + 84*x^82 + 63*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 99*x^75 + 36*x^74 + 21*x^73 + 86*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 2*x^68 + 71*x^67 + 124*x^66 + 33*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 121*x^27 + 60*x^26 + 15*x^25 + 82*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 102*x^20 + 29*x^19 + 100*x^18 + 123*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 7*x^11 + 20*x^10 + 17*x^9 + 30*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 26*x^4 + 59*x^3 + 12*x^2 + 13*x + 30, x^95 + 15*x^93 + 46*x^92 + 5*x^91 + 44*x^90 + 99*x^89 + 74*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 46*x^84 + 121*x^83 + 116*x^82 + 63*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 99*x^75 + 68*x^74 + 21*x^73 + 54*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 66*x^68 + 71*x^67 + 92*x^66 + 33*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 121*x^27 + 28*x^26 + 15*x^25 + 114*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 38*x^20 + 29*x^19 + 4*x^18 + 123*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 7*x^11 + 52*x^10 + 17*x^9 + 126*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 90*x^4 + 59*x^3 + 108*x^2 + 13*x + 62, x^95 + 15*x^93 + 50*x^92 + 101*x^91 + 84*x^90 + 67*x^89 + 86*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 50*x^84 + 25*x^83 + 12*x^82 + 95*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 3*x^75 + 60*x^74 + 53*x^73 + 42*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 94*x^68 + 39*x^67 + 36*x^66 + x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 89*x^27 + 100*x^26 + 111*x^25 + 46*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 58*x^20 + 61*x^19 + 124*x^18 + 27*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 39*x^11 + 76*x^10 + 49*x^9 + 98*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 70*x^4 + 27*x^3 + 20*x^2 + 109*x + 34, x^95 + 15*x^93 + 18*x^92 + 21*x^91 + 100*x^90 + 83*x^89 + 38*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 50*x^84 + 41*x^83 + 60*x^82 + 15*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 19*x^75 + 108*x^74 + 101*x^73 + 26*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 30*x^68 + 87*x^67 + 52*x^66 + 17*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 73*x^27 + 52*x^26 + 63*x^25 + 62*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 58*x^20 + 13*x^19 + 108*x^18 + 11*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 119*x^11 + 60*x^10 + 33*x^9 + 18*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 6*x^4 + 11*x^3 + 100*x^2 + 61*x + 114, x^95 + 15*x^93 + 94*x^92 + 5*x^91 + 44*x^90 + 35*x^89 + 122*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 30*x^84 + 121*x^83 + 116*x^82 + 127*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 99*x^75 + 68*x^74 + 85*x^73 + 6*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 82*x^68 + 71*x^67 + 92*x^66 + 97*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 121*x^27 + 28*x^26 + 79*x^25 + 98*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 86*x^20 + 29*x^19 + 4*x^18 + 59*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 7*x^11 + 52*x^10 + 81*x^9 + 14*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 42*x^4 + 59*x^3 + 108*x^2 + 77*x + 14, x^95 + 15*x^93 + 118*x^92 + 5*x^91 + 12*x^90 + 67*x^89 + 50*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 86*x^84 + 121*x^83 + 84*x^82 + 95*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 99*x^75 + 100*x^74 + 53*x^73 + 14*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 26*x^68 + 71*x^67 + 124*x^66 + x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 121*x^27 + 124*x^26 + 111*x^25 + 122*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 110*x^20 + 29*x^19 + 100*x^18 + 27*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 7*x^11 + 84*x^10 + 49*x^9 + 118*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 82*x^4 + 59*x^3 + 12*x^2 + 109*x + 22, x^95 + 15*x^93 + 122*x^92 + 85*x^91 + 36*x^90 + 115*x^89 + 14*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 58*x^84 + 105*x^83 + 60*x^82 + 111*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 83*x^75 + 44*x^74 + 69*x^73 + 114*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 22*x^68 + 23*x^67 + 52*x^66 + 49*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 9*x^27 + 116*x^26 + 95*x^25 + 70*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 98*x^20 + 77*x^19 + 108*x^18 + 107*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 55*x^11 + 124*x^10 + x^9 + 10*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 30*x^4 + 75*x^3 + 100*x^2 + 93*x + 10, x^95 + 15*x^93 + 6*x^92 + 5*x^91 + 44*x^90 + 3*x^89 + 34*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 102*x^84 + 121*x^83 + 52*x^82 + 31*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 99*x^75 + 68*x^74 + 117*x^73 + 30*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 10*x^68 + 71*x^67 + 28*x^66 + 65*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 121*x^27 + 28*x^26 + 47*x^25 + 42*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 62*x^20 + 29*x^19 + 68*x^18 + 91*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 7*x^11 + 52*x^10 + 113*x^9 + 70*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 2*x^4 + 59*x^3 + 44*x^2 + 45*x + 102, x^95 + 15*x^93 + 90*x^92 + 37*x^91 + 52*x^90 + 35*x^89 + 30*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 58*x^84 + 89*x^83 + 108*x^82 + 127*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 67*x^75 + 92*x^74 + 85*x^73 + 34*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 86*x^68 + 103*x^67 + 68*x^66 + 97*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 25*x^27 + 68*x^26 + 79*x^25 + 22*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 98*x^20 + 125*x^19 + 92*x^18 + 59*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 103*x^11 + 108*x^10 + 81*x^9 + 122*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 94*x^4 + 91*x^3 + 52*x^2 + 77*x + 26, x^95 + 15*x^93 + 54*x^92 + 5*x^91 + 44*x^90 + 3*x^89 + 18*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 86*x^84 + 121*x^83 + 52*x^82 + 31*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 99*x^75 + 68*x^74 + 117*x^73 + 46*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 26*x^68 + 71*x^67 + 28*x^66 + 65*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 121*x^27 + 28*x^26 + 47*x^25 + 90*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 110*x^20 + 29*x^19 + 68*x^18 + 91*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 7*x^11 + 52*x^10 + 113*x^9 + 22*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 82*x^4 + 59*x^3 + 44*x^2 + 45*x + 118, x^95 + 15*x^93 + 74*x^92 + 5*x^91 + 116*x^90 + 67*x^89 + 14*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 106*x^84 + 121*x^83 + 44*x^82 + 95*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 99*x^75 + 28*x^74 + 53*x^73 + 50*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 38*x^68 + 71*x^67 + 4*x^66 + x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 121*x^27 + 4*x^26 + 111*x^25 + 70*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 82*x^20 + 29*x^19 + 28*x^18 + 27*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 7*x^11 + 44*x^10 + 49*x^9 + 74*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 110*x^4 + 59*x^3 + 116*x^2 + 109*x + 42, x^95 + 15*x^93 + 86*x^92 + 21*x^91 + 92*x^90 + 115*x^89 + 66*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 86*x^84 + 41*x^83 + 68*x^82 + 111*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 19*x^75 + 84*x^74 + 69*x^73 + 62*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 90*x^68 + 87*x^67 + 76*x^66 + 49*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 73*x^27 + 12*x^26 + 95*x^25 + 74*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 110*x^20 + 13*x^19 + 20*x^18 + 107*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 119*x^11 + 4*x^10 + x^9 + 102*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 18*x^4 + 11*x^3 + 28*x^2 + 93*x + 38, x^95 + 15*x^93 + 14*x^92 + 117*x^91 + 60*x^90 + 115*x^89 + 90*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 46*x^84 + 73*x^83 + 36*x^82 + 111*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 51*x^75 + 116*x^74 + 69*x^73 + 102*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 2*x^68 + 55*x^67 + 108*x^66 + 49*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 41*x^27 + 108*x^26 + 95*x^25 + 66*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 38*x^20 + 45*x^19 + 116*x^18 + 107*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 23*x^11 + 36*x^10 + x^9 + 110*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 26*x^4 + 107*x^3 + 60*x^2 + 93*x + 78, x^95 + 15*x^93 + 30*x^92 + 117*x^91 + 92*x^90 + 115*x^89 + 10*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 62*x^84 + 73*x^83 + 4*x^82 + 111*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 51*x^75 + 84*x^74 + 69*x^73 + 54*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 114*x^68 + 55*x^67 + 12*x^66 + 49*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 41*x^27 + 12*x^26 + 95*x^25 + 50*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 118*x^20 + 45*x^19 + 84*x^18 + 107*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 23*x^11 + 4*x^10 + x^9 + 126*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 74*x^4 + 107*x^3 + 92*x^2 + 93*x + 94, x^95 + 15*x^93 + 38*x^92 + 5*x^91 + 44*x^90 + 3*x^89 + 66*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 6*x^84 + 121*x^83 + 52*x^82 + 31*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 99*x^75 + 68*x^74 + 117*x^73 + 126*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 106*x^68 + 71*x^67 + 28*x^66 + 65*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 121*x^27 + 28*x^26 + 47*x^25 + 74*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 94*x^20 + 29*x^19 + 68*x^18 + 91*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 7*x^11 + 52*x^10 + 113*x^9 + 38*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 98*x^4 + 59*x^3 + 44*x^2 + 45*x + 70, x^95 + 15*x^93 + 26*x^92 + 21*x^91 + 68*x^90 + 51*x^89 + 14*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 26*x^84 + 41*x^83 + 28*x^82 + 47*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 19*x^75 + 12*x^74 + 5*x^73 + 114*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 54*x^68 + 87*x^67 + 84*x^66 + 113*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 73*x^27 + 20*x^26 + 31*x^25 + 70*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 66*x^20 + 13*x^19 + 76*x^18 + 43*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 119*x^11 + 92*x^10 + 65*x^9 + 10*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 62*x^4 + 11*x^3 + 4*x^2 + 29*x + 74, x^95 + 15*x^93 + 110*x^92 + 117*x^91 + 124*x^90 + 51*x^89 + 58*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 14*x^84 + 73*x^83 + 100*x^82 + 47*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 51*x^75 + 52*x^74 + 5*x^73 + 6*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 34*x^68 + 55*x^67 + 44*x^66 + 113*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 41*x^27 + 44*x^26 + 31*x^25 + 34*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 6*x^20 + 45*x^19 + 52*x^18 + 43*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 23*x^11 + 100*x^10 + 65*x^9 + 14*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 58*x^4 + 107*x^3 + 124*x^2 + 29*x + 110, x^95 + 15*x^93 + 18*x^92 + 5*x^91 + 84*x^90 + 35*x^89 + 54*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 18*x^84 + 121*x^83 + 12*x^82 + 127*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 99*x^75 + 60*x^74 + 85*x^73 + 74*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 126*x^68 + 71*x^67 + 36*x^66 + 97*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 121*x^27 + 100*x^26 + 79*x^25 + 14*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 26*x^20 + 29*x^19 + 124*x^18 + 59*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 7*x^11 + 76*x^10 + 81*x^9 + 2*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 102*x^4 + 59*x^3 + 20*x^2 + 77*x + 66, x^95 + 15*x^93 + 126*x^92 + 117*x^91 + 92*x^90 + 115*x^89 + 106*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 30*x^84 + 73*x^83 + 4*x^82 + 111*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 51*x^75 + 84*x^74 + 69*x^73 + 86*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 18*x^68 + 55*x^67 + 12*x^66 + 49*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 41*x^27 + 12*x^26 + 95*x^25 + 18*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 86*x^20 + 45*x^19 + 84*x^18 + 107*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 23*x^11 + 4*x^10 + x^9 + 30*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 106*x^4 + 107*x^3 + 92*x^2 + 93*x + 126, x^95 + 15*x^93 + 102*x^92 + 37*x^91 + 44*x^90 + 35*x^89 + 66*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 70*x^84 + 89*x^83 + 52*x^82 + 127*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 67*x^75 + 68*x^74 + 85*x^73 + 126*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 42*x^68 + 103*x^67 + 28*x^66 + 97*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 25*x^27 + 28*x^26 + 79*x^25 + 74*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 30*x^20 + 125*x^19 + 68*x^18 + 59*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 103*x^11 + 52*x^10 + 81*x^9 + 38*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 34*x^4 + 91*x^3 + 44*x^2 + 77*x + 70, x^95 + 15*x^93 + 50*x^92 + 101*x^91 + 116*x^90 + 67*x^89 + 54*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 114*x^84 + 25*x^83 + 108*x^82 + 95*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 3*x^75 + 28*x^74 + 53*x^73 + 74*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 30*x^68 + 39*x^67 + 68*x^66 + x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 89*x^27 + 4*x^26 + 111*x^25 + 14*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 122*x^20 + 61*x^19 + 92*x^18 + 27*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 39*x^11 + 44*x^10 + 49*x^9 + 2*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 6*x^4 + 27*x^3 + 52*x^2 + 109*x + 2, x^95 + 15*x^93 + 98*x^92 + 5*x^91 + 116*x^90 + 35*x^89 + 38*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 98*x^84 + 121*x^83 + 108*x^82 + 127*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 99*x^75 + 28*x^74 + 85*x^73 + 90*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 46*x^68 + 71*x^67 + 68*x^66 + 97*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 121*x^27 + 4*x^26 + 79*x^25 + 62*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 42*x^20 + 29*x^19 + 92*x^18 + 59*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 7*x^11 + 44*x^10 + 81*x^9 + 82*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 86*x^4 + 59*x^3 + 52*x^2 + 77*x + 18, x^95 + 15*x^93 + 90*x^92 + 37*x^91 + 52*x^90 + 99*x^89 + 94*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 58*x^84 + 89*x^83 + 108*x^82 + 63*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 67*x^75 + 92*x^74 + 21*x^73 + 98*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 86*x^68 + 103*x^67 + 68*x^66 + 33*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 25*x^27 + 68*x^26 + 15*x^25 + 86*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 98*x^20 + 125*x^19 + 92*x^18 + 123*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 103*x^11 + 108*x^10 + 17*x^9 + 58*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 94*x^4 + 91*x^3 + 52*x^2 + 13*x + 90, x^95 + 15*x^93 + 106*x^92 + 53*x^91 + 100*x^90 + 19*x^89 + 126*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 106*x^84 + 9*x^83 + 124*x^82 + 79*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 115*x^75 + 108*x^74 + 37*x^73 + 2*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 102*x^68 + 119*x^67 + 116*x^66 + 81*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 105*x^27 + 52*x^26 + 127*x^25 + 118*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 82*x^20 + 109*x^19 + 44*x^18 + 75*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 87*x^11 + 60*x^10 + 97*x^9 + 90*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 46*x^4 + 43*x^3 + 36*x^2 + 125*x + 26, x^95 + 15*x^93 + 54*x^92 + 117*x^91 + 92*x^90 + 83*x^89 + 98*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 54*x^84 + 73*x^83 + 68*x^82 + 15*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 51*x^75 + 84*x^74 + 101*x^73 + 30*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 122*x^68 + 55*x^67 + 76*x^66 + 17*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 41*x^27 + 12*x^26 + 63*x^25 + 106*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 78*x^20 + 45*x^19 + 20*x^18 + 11*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 23*x^11 + 4*x^10 + 33*x^9 + 70*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 50*x^4 + 107*x^3 + 28*x^2 + 61*x + 6, x^95 + 15*x^93 + 106*x^92 + 101*x^91 + 116*x^90 + 99*x^89 + 46*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 10*x^84 + 25*x^83 + 44*x^82 + 63*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 3*x^75 + 28*x^74 + 21*x^73 + 18*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 6*x^68 + 39*x^67 + 4*x^66 + 33*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 89*x^27 + 4*x^26 + 15*x^25 + 102*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 114*x^20 + 61*x^19 + 28*x^18 + 123*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 39*x^11 + 44*x^10 + 17*x^9 + 42*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 78*x^4 + 27*x^3 + 116*x^2 + 13*x + 10, x^95 + 15*x^93 + 50*x^92 + 5*x^91 + 84*x^90 + 99*x^89 + 22*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 50*x^84 + 121*x^83 + 12*x^82 + 63*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 99*x^75 + 60*x^74 + 21*x^73 + 106*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 94*x^68 + 71*x^67 + 36*x^66 + 33*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 121*x^27 + 100*x^26 + 15*x^25 + 110*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 58*x^20 + 29*x^19 + 124*x^18 + 123*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 7*x^11 + 76*x^10 + 17*x^9 + 34*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 70*x^4 + 59*x^3 + 20*x^2 + 13*x + 98, x^95 + 15*x^93 + 86*x^92 + 101*x^91 + 44*x^90 + 99*x^89 + 114*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 118*x^84 + 25*x^83 + 52*x^82 + 63*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 3*x^75 + 68*x^74 + 21*x^73 + 78*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 122*x^68 + 39*x^67 + 28*x^66 + 33*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 89*x^27 + 28*x^26 + 15*x^25 + 58*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 14*x^20 + 61*x^19 + 68*x^18 + 123*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 39*x^11 + 52*x^10 + 17*x^9 + 54*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 50*x^4 + 27*x^3 + 44*x^2 + 13*x + 22, x^95 + 15*x^93 + 42*x^92 + 21*x^91 + 68*x^90 + 115*x^89 + 30*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 106*x^84 + 41*x^83 + 28*x^82 + 111*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 19*x^75 + 12*x^74 + 69*x^73 + 98*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 102*x^68 + 87*x^67 + 84*x^66 + 49*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 73*x^27 + 20*x^26 + 95*x^25 + 22*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 82*x^20 + 13*x^19 + 76*x^18 + 107*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 119*x^11 + 92*x^10 + x^9 + 58*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 46*x^4 + 11*x^3 + 4*x^2 + 93*x + 58, x^95 + 15*x^93 + 6*x^92 + 37*x^91 + 76*x^90 + 99*x^89 + 2*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 38*x^84 + 89*x^83 + 20*x^82 + 63*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 67*x^75 + 36*x^74 + 21*x^73 + 62*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 74*x^68 + 103*x^67 + 60*x^66 + 33*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 25*x^27 + 60*x^26 + 15*x^25 + 10*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 126*x^20 + 125*x^19 + 36*x^18 + 123*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 103*x^11 + 20*x^10 + 17*x^9 + 102*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 66*x^4 + 91*x^3 + 76*x^2 + 13*x + 70, x^95 + 15*x^93 + 2*x^92 + 117*x^91 + 68*x^90 + 51*x^89 + 54*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 34*x^84 + 73*x^83 + 92*x^82 + 47*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 51*x^75 + 12*x^74 + 5*x^73 + 10*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 46*x^68 + 55*x^67 + 20*x^66 + 113*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 41*x^27 + 20*x^26 + 31*x^25 + 14*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 106*x^20 + 45*x^19 + 12*x^18 + 43*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 23*x^11 + 92*x^10 + 65*x^9 + 66*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 86*x^4 + 107*x^3 + 68*x^2 + 29*x + 34, x^95 + 15*x^93 + 22*x^92 + 5*x^91 + 12*x^90 + 3*x^89 + 18*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 118*x^84 + 121*x^83 + 84*x^82 + 31*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 99*x^75 + 100*x^74 + 117*x^73 + 46*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 122*x^68 + 71*x^67 + 124*x^66 + 65*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 121*x^27 + 124*x^26 + 47*x^25 + 90*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 14*x^20 + 29*x^19 + 100*x^18 + 91*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 7*x^11 + 84*x^10 + 113*x^9 + 22*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 50*x^4 + 59*x^3 + 12*x^2 + 45*x + 54, x^95 + 15*x^93 + 30*x^92 + 21*x^91 + 60*x^90 + 19*x^89 + 106*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 126*x^84 + 41*x^83 + 36*x^82 + 79*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 19*x^75 + 116*x^74 + 37*x^73 + 86*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 50*x^68 + 87*x^67 + 108*x^66 + 81*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 73*x^27 + 108*x^26 + 127*x^25 + 18*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 54*x^20 + 13*x^19 + 116*x^18 + 75*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 119*x^11 + 36*x^10 + 97*x^9 + 30*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 10*x^4 + 11*x^3 + 60*x^2 + 125*x + 62, x^95 + 15*x^93 + 46*x^92 + 85*x^91 + 60*x^90 + 83*x^89 + 58*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 78*x^84 + 105*x^83 + 36*x^82 + 15*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 83*x^75 + 116*x^74 + 101*x^73 + 6*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 98*x^68 + 23*x^67 + 108*x^66 + 17*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 9*x^27 + 108*x^26 + 63*x^25 + 34*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 70*x^20 + 77*x^19 + 116*x^18 + 11*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 55*x^11 + 36*x^10 + 33*x^9 + 14*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 122*x^4 + 75*x^3 + 60*x^2 + 61*x + 110, x^95 + 15*x^93 + 126*x^92 + 53*x^91 + 124*x^90 + 51*x^89 + 74*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 94*x^84 + 9*x^83 + 100*x^82 + 47*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 115*x^75 + 52*x^74 + 5*x^73 + 118*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 82*x^68 + 119*x^67 + 44*x^66 + 113*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 105*x^27 + 44*x^26 + 31*x^25 + 114*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 22*x^20 + 109*x^19 + 52*x^18 + 43*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 87*x^11 + 100*x^10 + 65*x^9 + 62*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 42*x^4 + 43*x^3 + 124*x^2 + 29*x + 94, x^95 + 15*x^93 + 74*x^92 + 21*x^91 + 36*x^90 + 115*x^89 + 94*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 74*x^84 + 41*x^83 + 60*x^82 + 111*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 19*x^75 + 44*x^74 + 69*x^73 + 34*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 6*x^68 + 87*x^67 + 52*x^66 + 49*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 73*x^27 + 116*x^26 + 95*x^25 + 86*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 50*x^20 + 13*x^19 + 108*x^18 + 107*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 119*x^11 + 124*x^10 + x^9 + 122*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 78*x^4 + 11*x^3 + 100*x^2 + 93*x + 58, x^95 + 15*x^93 + 34*x^92 + 117*x^91 + 4*x^90 + 115*x^89 + 86*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 66*x^84 + 73*x^83 + 28*x^82 + 111*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 51*x^75 + 76*x^74 + 69*x^73 + 106*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 14*x^68 + 55*x^67 + 84*x^66 + 49*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 41*x^27 + 84*x^26 + 95*x^25 + 46*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 10*x^20 + 45*x^19 + 76*x^18 + 107*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 23*x^11 + 28*x^10 + x^9 + 34*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 54*x^4 + 107*x^3 + 4*x^2 + 93*x + 2, x^95 + 15*x^93 + 98*x^92 + 69*x^91 + 84*x^90 + 35*x^89 + 6*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 34*x^84 + 57*x^83 + 12*x^82 + 127*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 35*x^75 + 60*x^74 + 85*x^73 + 122*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 110*x^68 + 7*x^67 + 36*x^66 + 97*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 57*x^27 + 100*x^26 + 79*x^25 + 30*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 106*x^20 + 93*x^19 + 124*x^18 + 59*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 71*x^11 + 76*x^10 + 81*x^9 + 114*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 22*x^4 + 123*x^3 + 20*x^2 + 77*x + 114, x^95 + 15*x^93 + 46*x^92 + 37*x^91 + 44*x^90 + 3*x^89 + 10*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 46*x^84 + 89*x^83 + 116*x^82 + 31*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 67*x^75 + 68*x^74 + 117*x^73 + 118*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 66*x^68 + 103*x^67 + 92*x^66 + 65*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 25*x^27 + 28*x^26 + 47*x^25 + 50*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 38*x^20 + 125*x^19 + 4*x^18 + 91*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 103*x^11 + 52*x^10 + 113*x^9 + 62*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 90*x^4 + 91*x^3 + 108*x^2 + 45*x + 126, x^95 + 15*x^93 + 26*x^92 + 21*x^91 + 100*x^90 + 115*x^89 + 46*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 90*x^84 + 41*x^83 + 124*x^82 + 111*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 19*x^75 + 108*x^74 + 69*x^73 + 82*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 118*x^68 + 87*x^67 + 116*x^66 + 49*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 73*x^27 + 52*x^26 + 95*x^25 + 102*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 2*x^20 + 13*x^19 + 44*x^18 + 107*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 119*x^11 + 60*x^10 + x^9 + 106*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 126*x^4 + 11*x^3 + 36*x^2 + 93*x + 106, x^95 + 15*x^93 + 98*x^92 + 85*x^91 + 68*x^90 + 19*x^89 + 86*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 2*x^84 + 105*x^83 + 92*x^82 + 79*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 83*x^75 + 12*x^74 + 37*x^73 + 106*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 78*x^68 + 23*x^67 + 20*x^66 + 81*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 9*x^27 + 20*x^26 + 127*x^25 + 46*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 74*x^20 + 77*x^19 + 12*x^18 + 75*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 55*x^11 + 92*x^10 + 97*x^9 + 34*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 118*x^4 + 75*x^3 + 68*x^2 + 125*x + 2, x^95 + 15*x^93 + 62*x^92 + 117*x^91 + 28*x^90 + 115*x^89 + 106*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 94*x^84 + 73*x^83 + 68*x^82 + 111*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 51*x^75 + 20*x^74 + 69*x^73 + 86*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 82*x^68 + 55*x^67 + 76*x^66 + 49*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 41*x^27 + 76*x^26 + 95*x^25 + 18*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 22*x^20 + 45*x^19 + 20*x^18 + 107*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 23*x^11 + 68*x^10 + x^9 + 30*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 42*x^4 + 107*x^3 + 28*x^2 + 93*x + 126, x^95 + 15*x^93 + 126*x^92 + 69*x^91 + 44*x^90 + 99*x^89 + 26*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 62*x^84 + 57*x^83 + 116*x^82 + 63*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 35*x^75 + 68*x^74 + 21*x^73 + 102*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 50*x^68 + 7*x^67 + 92*x^66 + 33*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 57*x^27 + 28*x^26 + 15*x^25 + 2*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 118*x^20 + 93*x^19 + 4*x^18 + 123*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 71*x^11 + 52*x^10 + 17*x^9 + 110*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 10*x^4 + 123*x^3 + 108*x^2 + 13*x + 110, x^95 + 15*x^93 + 10*x^92 + 5*x^91 + 116*x^90 + 3*x^89 + 14*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 42*x^84 + 121*x^83 + 44*x^82 + 31*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 99*x^75 + 28*x^74 + 117*x^73 + 50*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 102*x^68 + 71*x^67 + 4*x^66 + 65*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 121*x^27 + 4*x^26 + 47*x^25 + 70*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 18*x^20 + 29*x^19 + 28*x^18 + 91*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 7*x^11 + 44*x^10 + 113*x^9 + 74*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 46*x^4 + 59*x^3 + 116*x^2 + 45*x + 42, x^95 + 15*x^93 + 54*x^92 + 37*x^91 + 108*x^90 + 99*x^89 + 82*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 86*x^84 + 89*x^83 + 116*x^82 + 63*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 67*x^75 + 4*x^74 + 21*x^73 + 110*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 26*x^68 + 103*x^67 + 92*x^66 + 33*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 25*x^27 + 92*x^26 + 15*x^25 + 26*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 110*x^20 + 125*x^19 + 4*x^18 + 123*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 103*x^11 + 116*x^10 + 17*x^9 + 86*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 82*x^4 + 91*x^3 + 108*x^2 + 13*x + 54, x^95 + 15*x^93 + 110*x^92 + 85*x^91 + 60*x^90 + 83*x^89 + 122*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 14*x^84 + 105*x^83 + 36*x^82 + 15*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 83*x^75 + 116*x^74 + 101*x^73 + 70*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 34*x^68 + 23*x^67 + 108*x^66 + 17*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 9*x^27 + 108*x^26 + 63*x^25 + 98*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 6*x^20 + 77*x^19 + 116*x^18 + 11*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 55*x^11 + 36*x^10 + 33*x^9 + 78*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 58*x^4 + 75*x^3 + 60*x^2 + 61*x + 46, x^95 + 15*x^93 + 82*x^92 + 53*x^91 + 68*x^90 + 115*x^89 + 70*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 50*x^84 + 9*x^83 + 92*x^82 + 111*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 115*x^75 + 12*x^74 + 69*x^73 + 122*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 30*x^68 + 119*x^67 + 20*x^66 + 49*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 105*x^27 + 20*x^26 + 95*x^25 + 94*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 58*x^20 + 109*x^19 + 12*x^18 + 107*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 87*x^11 + 92*x^10 + x^9 + 114*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 6*x^4 + 43*x^3 + 68*x^2 + 93*x + 18, x^95 + 15*x^93 + 38*x^92 + 69*x^91 + 44*x^90 + 67*x^89 + 66*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 6*x^84 + 57*x^83 + 52*x^82 + 95*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 35*x^75 + 68*x^74 + 53*x^73 + 126*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 106*x^68 + 7*x^67 + 28*x^66 + x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 57*x^27 + 28*x^26 + 111*x^25 + 74*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 94*x^20 + 93*x^19 + 68*x^18 + 27*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 71*x^11 + 52*x^10 + 49*x^9 + 38*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 98*x^4 + 123*x^3 + 44*x^2 + 109*x + 70, x^95 + 15*x^93 + 90*x^92 + 85*x^91 + 100*x^90 + 51*x^89 + 110*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 26*x^84 + 105*x^83 + 124*x^82 + 47*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 83*x^75 + 108*x^74 + 5*x^73 + 18*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 54*x^68 + 23*x^67 + 116*x^66 + 113*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 9*x^27 + 52*x^26 + 31*x^25 + 38*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 66*x^20 + 77*x^19 + 44*x^18 + 43*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 55*x^11 + 60*x^10 + 65*x^9 + 42*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 62*x^4 + 75*x^3 + 36*x^2 + 29*x + 42, x^95 + 15*x^93 + 10*x^92 + 21*x^91 + 4*x^90 + 115*x^89 + 62*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 74*x^84 + 41*x^83 + 92*x^82 + 111*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 19*x^75 + 76*x^74 + 69*x^73 + 66*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 6*x^68 + 87*x^67 + 20*x^66 + 49*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 73*x^27 + 84*x^26 + 95*x^25 + 54*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 50*x^20 + 13*x^19 + 12*x^18 + 107*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 119*x^11 + 28*x^10 + x^9 + 26*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 78*x^4 + 11*x^3 + 68*x^2 + 93*x + 26, x^95 + 15*x^93 + 22*x^92 + 21*x^91 + 28*x^90 + 115*x^89 + 66*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 22*x^84 + 41*x^83 + 4*x^82 + 111*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 19*x^75 + 20*x^74 + 69*x^73 + 62*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 26*x^68 + 87*x^67 + 12*x^66 + 49*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 73*x^27 + 76*x^26 + 95*x^25 + 74*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 46*x^20 + 13*x^19 + 84*x^18 + 107*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 119*x^11 + 68*x^10 + x^9 + 102*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 82*x^4 + 11*x^3 + 92*x^2 + 93*x + 38, x^95 + 15*x^93 + 38*x^92 + 101*x^91 + 44*x^90 + 99*x^89 + 2*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 6*x^84 + 25*x^83 + 52*x^82 + 63*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 3*x^75 + 68*x^74 + 21*x^73 + 62*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 106*x^68 + 39*x^67 + 28*x^66 + 33*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 89*x^27 + 28*x^26 + 15*x^25 + 10*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 94*x^20 + 61*x^19 + 68*x^18 + 123*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 39*x^11 + 52*x^10 + 17*x^9 + 102*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 98*x^4 + 27*x^3 + 44*x^2 + 13*x + 6, x^95 + 15*x^93 + 86*x^92 + 21*x^91 + 124*x^90 + 115*x^89 + 34*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 22*x^84 + 41*x^83 + 36*x^82 + 111*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 19*x^75 + 52*x^74 + 69*x^73 + 94*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 26*x^68 + 87*x^67 + 108*x^66 + 49*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 73*x^27 + 44*x^26 + 95*x^25 + 42*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 46*x^20 + 13*x^19 + 116*x^18 + 107*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 119*x^11 + 100*x^10 + x^9 + 6*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 82*x^4 + 11*x^3 + 60*x^2 + 93*x + 6, x^95 + 15*x^93 + 26*x^92 + 5*x^91 + 20*x^90 + 3*x^89 + 62*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 58*x^84 + 121*x^83 + 12*x^82 + 31*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 99*x^75 + 124*x^74 + 117*x^73 + 2*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 86*x^68 + 71*x^67 + 36*x^66 + 65*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 121*x^27 + 36*x^26 + 47*x^25 + 54*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 98*x^20 + 29*x^19 + 124*x^18 + 91*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 7*x^11 + 12*x^10 + 113*x^9 + 90*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 94*x^4 + 59*x^3 + 20*x^2 + 45*x + 58, x^95 + 15*x^93 + 90*x^92 + 5*x^91 + 52*x^90 + 3*x^89 + 94*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 58*x^84 + 121*x^83 + 108*x^82 + 31*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 99*x^75 + 92*x^74 + 117*x^73 + 98*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 86*x^68 + 71*x^67 + 68*x^66 + 65*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 121*x^27 + 68*x^26 + 47*x^25 + 86*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 98*x^20 + 29*x^19 + 92*x^18 + 91*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 7*x^11 + 108*x^10 + 113*x^9 + 58*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 94*x^4 + 59*x^3 + 52*x^2 + 45*x + 90, x^95 + 15*x^93 + 46*x^92 + 117*x^91 + 124*x^90 + 51*x^89 + 122*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 78*x^84 + 73*x^83 + 100*x^82 + 47*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 51*x^75 + 52*x^74 + 5*x^73 + 70*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 98*x^68 + 55*x^67 + 44*x^66 + 113*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 41*x^27 + 44*x^26 + 31*x^25 + 98*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 70*x^20 + 45*x^19 + 52*x^18 + 43*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 23*x^11 + 100*x^10 + 65*x^9 + 78*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 122*x^4 + 107*x^3 + 124*x^2 + 29*x + 46, x^95 + 15*x^93 + 6*x^92 + 85*x^91 + 124*x^90 + 51*x^89 + 18*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 6*x^84 + 105*x^83 + 36*x^82 + 47*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 83*x^75 + 52*x^74 + 5*x^73 + 110*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 42*x^68 + 23*x^67 + 108*x^66 + 113*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 9*x^27 + 44*x^26 + 31*x^25 + 90*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 94*x^20 + 77*x^19 + 116*x^18 + 43*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 55*x^11 + 100*x^10 + 65*x^9 + 86*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 34*x^4 + 75*x^3 + 60*x^2 + 29*x + 22, x^95 + 15*x^93 + 2*x^92 + 5*x^91 + 20*x^90 + 99*x^89 + 102*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 66*x^84 + 121*x^83 + 76*x^82 + 63*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 99*x^75 + 124*x^74 + 21*x^73 + 26*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 78*x^68 + 71*x^67 + 100*x^66 + 33*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 121*x^27 + 36*x^26 + 15*x^25 + 126*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 10*x^20 + 29*x^19 + 60*x^18 + 123*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 7*x^11 + 12*x^10 + 17*x^9 + 18*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 118*x^4 + 59*x^3 + 84*x^2 + 13*x + 18, x^95 + 15*x^93 + 106*x^92 + 85*x^91 + 100*x^90 + 51*x^89 + 62*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 106*x^84 + 105*x^83 + 124*x^82 + 47*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 83*x^75 + 108*x^74 + 5*x^73 + 66*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 102*x^68 + 23*x^67 + 116*x^66 + 113*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 9*x^27 + 52*x^26 + 31*x^25 + 54*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 82*x^20 + 77*x^19 + 44*x^18 + 43*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 55*x^11 + 60*x^10 + 65*x^9 + 26*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 46*x^4 + 75*x^3 + 36*x^2 + 29*x + 90, x^95 + 15*x^93 + 6*x^92 + 5*x^91 + 108*x^90 + 3*x^89 + 98*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 102*x^84 + 121*x^83 + 116*x^82 + 31*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 99*x^75 + 4*x^74 + 117*x^73 + 94*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 10*x^68 + 71*x^67 + 92*x^66 + 65*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 121*x^27 + 92*x^26 + 47*x^25 + 106*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 62*x^20 + 29*x^19 + 4*x^18 + 91*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 7*x^11 + 116*x^10 + 113*x^9 + 6*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 2*x^4 + 59*x^3 + 108*x^2 + 45*x + 38, x^95 + 15*x^93 + 54*x^92 + 5*x^91 + 76*x^90 + 3*x^89 + 114*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 22*x^84 + 121*x^83 + 20*x^82 + 31*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 99*x^75 + 36*x^74 + 117*x^73 + 78*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 90*x^68 + 71*x^67 + 60*x^66 + 65*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 121*x^27 + 60*x^26 + 47*x^25 + 58*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 46*x^20 + 29*x^19 + 36*x^18 + 91*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 7*x^11 + 20*x^10 + 113*x^9 + 54*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 18*x^4 + 59*x^3 + 76*x^2 + 45*x + 86, x^95 + 15*x^93 + 94*x^92 + 85*x^91 + 124*x^90 + 19*x^89 + 42*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 62*x^84 + 105*x^83 + 100*x^82 + 79*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 83*x^75 + 52*x^74 + 37*x^73 + 22*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 114*x^68 + 23*x^67 + 44*x^66 + 81*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 9*x^27 + 44*x^26 + 127*x^25 + 82*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 118*x^20 + 77*x^19 + 52*x^18 + 75*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 55*x^11 + 100*x^10 + 97*x^9 + 94*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 74*x^4 + 75*x^3 + 124*x^2 + 125*x + 126, x^95 + 15*x^93 + 74*x^92 + 53*x^91 + 68*x^90 + 19*x^89 + 126*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 10*x^84 + 9*x^83 + 28*x^82 + 79*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 115*x^75 + 12*x^74 + 37*x^73 + 2*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 70*x^68 + 119*x^67 + 84*x^66 + 81*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 105*x^27 + 20*x^26 + 127*x^25 + 118*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 114*x^20 + 109*x^19 + 76*x^18 + 75*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 87*x^11 + 92*x^10 + 97*x^9 + 90*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 14*x^4 + 43*x^3 + 4*x^2 + 125*x + 90, x^95 + 15*x^93 + 70*x^92 + 53*x^91 + 124*x^90 + 83*x^89 + 82*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 70*x^84 + 9*x^83 + 36*x^82 + 15*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 115*x^75 + 52*x^74 + 101*x^73 + 46*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 106*x^68 + 119*x^67 + 108*x^66 + 17*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 105*x^27 + 44*x^26 + 63*x^25 + 26*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 30*x^20 + 109*x^19 + 116*x^18 + 11*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 87*x^11 + 100*x^10 + 33*x^9 + 22*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 98*x^4 + 43*x^3 + 60*x^2 + 61*x + 86, x^95 + 15*x^93 + 18*x^92 + 5*x^91 + 52*x^90 + 99*x^89 + 22*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 82*x^84 + 121*x^83 + 44*x^82 + 63*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 99*x^75 + 92*x^74 + 21*x^73 + 106*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 62*x^68 + 71*x^67 + 4*x^66 + 33*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 121*x^27 + 68*x^26 + 15*x^25 + 110*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 90*x^20 + 29*x^19 + 28*x^18 + 123*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 7*x^11 + 108*x^10 + 17*x^9 + 34*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 38*x^4 + 59*x^3 + 116*x^2 + 13*x + 34, x^95 + 15*x^93 + 102*x^92 + 53*x^91 + 124*x^90 + 19*x^89 + 50*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 102*x^84 + 9*x^83 + 36*x^82 + 79*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 115*x^75 + 52*x^74 + 37*x^73 + 78*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 74*x^68 + 119*x^67 + 108*x^66 + 81*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 105*x^27 + 44*x^26 + 127*x^25 + 122*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 62*x^20 + 109*x^19 + 116*x^18 + 75*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 87*x^11 + 100*x^10 + 97*x^9 + 54*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 66*x^4 + 43*x^3 + 60*x^2 + 125*x + 118, x^95 + 15*x^93 + 10*x^92 + 69*x^91 + 116*x^90 + 67*x^89 + 14*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 42*x^84 + 57*x^83 + 44*x^82 + 95*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 35*x^75 + 28*x^74 + 53*x^73 + 50*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 102*x^68 + 7*x^67 + 4*x^66 + x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 57*x^27 + 4*x^26 + 111*x^25 + 70*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 18*x^20 + 93*x^19 + 28*x^18 + 27*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 71*x^11 + 44*x^10 + 49*x^9 + 74*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 46*x^4 + 123*x^3 + 116*x^2 + 109*x + 42, x^95 + 15*x^93 + 86*x^92 + 101*x^91 + 76*x^90 + 35*x^89 + 18*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 54*x^84 + 25*x^83 + 20*x^82 + 127*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 3*x^75 + 36*x^74 + 85*x^73 + 46*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 58*x^68 + 39*x^67 + 60*x^66 + 97*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 89*x^27 + 60*x^26 + 79*x^25 + 90*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 78*x^20 + 61*x^19 + 36*x^18 + 59*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 39*x^11 + 20*x^10 + 81*x^9 + 22*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 114*x^4 + 27*x^3 + 76*x^2 + 77*x + 54, x^95 + 15*x^93 + 94*x^92 + 101*x^91 + 76*x^90 + 67*x^89 + 90*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 94*x^84 + 25*x^83 + 84*x^82 + 95*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 3*x^75 + 36*x^74 + 53*x^73 + 38*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 18*x^68 + 39*x^67 + 124*x^66 + x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 89*x^27 + 60*x^26 + 111*x^25 + 66*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 22*x^20 + 61*x^19 + 100*x^18 + 27*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 39*x^11 + 20*x^10 + 49*x^9 + 46*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 106*x^4 + 27*x^3 + 12*x^2 + 109*x + 110, x^95 + 15*x^93 + 90*x^92 + 5*x^91 + 84*x^90 + 67*x^89 + 126*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 122*x^84 + 121*x^83 + 76*x^82 + 95*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 99*x^75 + 60*x^74 + 53*x^73 + 66*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 22*x^68 + 71*x^67 + 100*x^66 + x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 121*x^27 + 100*x^26 + 111*x^25 + 118*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 34*x^20 + 29*x^19 + 60*x^18 + 27*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 7*x^11 + 76*x^10 + 49*x^9 + 26*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 30*x^4 + 59*x^3 + 84*x^2 + 109*x + 122, x^95 + 15*x^93 + 58*x^92 + 53*x^91 + 100*x^90 + 19*x^89 + 14*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 122*x^84 + 9*x^83 + 124*x^82 + 79*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 115*x^75 + 108*x^74 + 37*x^73 + 114*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 86*x^68 + 119*x^67 + 116*x^66 + 81*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 105*x^27 + 52*x^26 + 127*x^25 + 70*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 34*x^20 + 109*x^19 + 44*x^18 + 75*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 87*x^11 + 60*x^10 + 97*x^9 + 10*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 94*x^4 + 43*x^3 + 36*x^2 + 125*x + 10, x^95 + 15*x^93 + 70*x^92 + 117*x^91 + 60*x^90 + 19*x^89 + 18*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 70*x^84 + 73*x^83 + 100*x^82 + 79*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 51*x^75 + 116*x^74 + 37*x^73 + 110*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 106*x^68 + 55*x^67 + 44*x^66 + 81*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 41*x^27 + 108*x^26 + 127*x^25 + 90*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 30*x^20 + 45*x^19 + 52*x^18 + 75*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 23*x^11 + 36*x^10 + 97*x^9 + 86*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 98*x^4 + 107*x^3 + 124*x^2 + 125*x + 22, x^95 + 15*x^93 + 58*x^92 + 117*x^91 + 36*x^90 + 83*x^89 + 78*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 122*x^84 + 73*x^83 + 60*x^82 + 15*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 51*x^75 + 44*x^74 + 101*x^73 + 50*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 86*x^68 + 55*x^67 + 52*x^66 + 17*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 41*x^27 + 116*x^26 + 63*x^25 + 6*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 34*x^20 + 45*x^19 + 108*x^18 + 11*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 23*x^11 + 124*x^10 + 33*x^9 + 74*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 94*x^4 + 107*x^3 + 100*x^2 + 61*x + 74, x^95 + 15*x^93 + 62*x^92 + 85*x^91 + 60*x^90 + 83*x^89 + 10*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 30*x^84 + 105*x^83 + 36*x^82 + 15*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 83*x^75 + 116*x^74 + 101*x^73 + 54*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 18*x^68 + 23*x^67 + 108*x^66 + 17*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 9*x^27 + 108*x^26 + 63*x^25 + 50*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 86*x^20 + 77*x^19 + 116*x^18 + 11*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 55*x^11 + 36*x^10 + 33*x^9 + 126*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 106*x^4 + 75*x^3 + 60*x^2 + 61*x + 30, x^95 + 15*x^93 + 94*x^92 + 69*x^91 + 108*x^90 + 35*x^89 + 122*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 30*x^84 + 57*x^83 + 52*x^82 + 127*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 35*x^75 + 4*x^74 + 85*x^73 + 6*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 82*x^68 + 7*x^67 + 28*x^66 + 97*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 57*x^27 + 92*x^26 + 79*x^25 + 98*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 86*x^20 + 93*x^19 + 68*x^18 + 59*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 71*x^11 + 116*x^10 + 81*x^9 + 14*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 42*x^4 + 123*x^3 + 44*x^2 + 77*x + 14, x^95 + 15*x^93 + 18*x^92 + 101*x^91 + 84*x^90 + 3*x^89 + 118*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 18*x^84 + 25*x^83 + 12*x^82 + 31*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 3*x^75 + 60*x^74 + 117*x^73 + 10*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 126*x^68 + 39*x^67 + 36*x^66 + 65*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 89*x^27 + 100*x^26 + 47*x^25 + 78*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 26*x^20 + 61*x^19 + 124*x^18 + 91*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 39*x^11 + 76*x^10 + 113*x^9 + 66*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 102*x^4 + 27*x^3 + 20*x^2 + 45*x + 2, x^95 + 15*x^93 + 6*x^92 + 37*x^91 + 12*x^90 + 35*x^89 + 2*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 38*x^84 + 89*x^83 + 84*x^82 + 127*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 67*x^75 + 100*x^74 + 85*x^73 + 62*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 74*x^68 + 103*x^67 + 124*x^66 + 97*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 25*x^27 + 124*x^26 + 79*x^25 + 10*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 126*x^20 + 125*x^19 + 100*x^18 + 59*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 103*x^11 + 84*x^10 + 81*x^9 + 102*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 66*x^4 + 91*x^3 + 12*x^2 + 77*x + 70, x^95 + 15*x^93 + 38*x^92 + 69*x^91 + 44*x^90 + 3*x^89 + 2*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 6*x^84 + 57*x^83 + 52*x^82 + 31*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 35*x^75 + 68*x^74 + 117*x^73 + 62*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 106*x^68 + 7*x^67 + 28*x^66 + 65*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 57*x^27 + 28*x^26 + 47*x^25 + 10*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 94*x^20 + 93*x^19 + 68*x^18 + 91*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 71*x^11 + 52*x^10 + 113*x^9 + 102*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 98*x^4 + 123*x^3 + 44*x^2 + 45*x + 6, x^95 + 15*x^93 + 122*x^92 + 21*x^91 + 68*x^90 + 115*x^89 + 46*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 122*x^84 + 41*x^83 + 28*x^82 + 111*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 19*x^75 + 12*x^74 + 69*x^73 + 82*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 86*x^68 + 87*x^67 + 84*x^66 + 49*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 73*x^27 + 20*x^26 + 95*x^25 + 102*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 34*x^20 + 13*x^19 + 76*x^18 + 107*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 119*x^11 + 92*x^10 + x^9 + 106*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 94*x^4 + 11*x^3 + 4*x^2 + 93*x + 42, x^95 + 15*x^93 + 14*x^92 + 53*x^91 + 28*x^90 + 51*x^89 + 122*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 110*x^84 + 9*x^83 + 68*x^82 + 47*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 115*x^75 + 20*x^74 + 5*x^73 + 70*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 66*x^68 + 119*x^67 + 76*x^66 + 113*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 105*x^27 + 76*x^26 + 31*x^25 + 98*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 102*x^20 + 109*x^19 + 20*x^18 + 43*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 87*x^11 + 68*x^10 + 65*x^9 + 78*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 90*x^4 + 43*x^3 + 28*x^2 + 29*x + 110, x^95 + 15*x^93 + 6*x^92 + 69*x^91 + 108*x^90 + 67*x^89 + 98*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 102*x^84 + 57*x^83 + 116*x^82 + 95*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 35*x^75 + 4*x^74 + 53*x^73 + 94*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 10*x^68 + 7*x^67 + 92*x^66 + x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 57*x^27 + 92*x^26 + 111*x^25 + 106*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 62*x^20 + 93*x^19 + 4*x^18 + 27*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 71*x^11 + 116*x^10 + 49*x^9 + 6*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 2*x^4 + 123*x^3 + 108*x^2 + 109*x + 38, x^95 + 15*x^93 + 18*x^92 + 5*x^91 + 20*x^90 + 35*x^89 + 118*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 18*x^84 + 121*x^83 + 76*x^82 + 127*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 99*x^75 + 124*x^74 + 85*x^73 + 10*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 126*x^68 + 71*x^67 + 100*x^66 + 97*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 121*x^27 + 36*x^26 + 79*x^25 + 78*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 26*x^20 + 29*x^19 + 60*x^18 + 59*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 7*x^11 + 12*x^10 + 81*x^9 + 66*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 102*x^4 + 59*x^3 + 84*x^2 + 77*x + 2, x^95 + 15*x^93 + 38*x^92 + 21*x^91 + 124*x^90 + 51*x^89 + 114*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 38*x^84 + 41*x^83 + 36*x^82 + 47*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 19*x^75 + 52*x^74 + 5*x^73 + 14*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 10*x^68 + 87*x^67 + 108*x^66 + 113*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 73*x^27 + 44*x^26 + 31*x^25 + 58*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 126*x^20 + 13*x^19 + 116*x^18 + 43*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 119*x^11 + 100*x^10 + 65*x^9 + 118*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 2*x^4 + 11*x^3 + 60*x^2 + 29*x + 54, x^95 + 15*x^93 + 110*x^92 + 101*x^91 + 12*x^90 + 3*x^89 + 42*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 46*x^84 + 25*x^83 + 20*x^82 + 31*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 3*x^75 + 100*x^74 + 117*x^73 + 86*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 66*x^68 + 39*x^67 + 60*x^66 + 65*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 89*x^27 + 124*x^26 + 47*x^25 + 82*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 38*x^20 + 61*x^19 + 36*x^18 + 91*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 39*x^11 + 84*x^10 + 113*x^9 + 30*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 90*x^4 + 27*x^3 + 76*x^2 + 45*x + 30, x^95 + 15*x^93 + 46*x^92 + 101*x^91 + 108*x^90 + 3*x^89 + 10*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 46*x^84 + 25*x^83 + 52*x^82 + 31*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 3*x^75 + 4*x^74 + 117*x^73 + 118*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 66*x^68 + 39*x^67 + 28*x^66 + 65*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 89*x^27 + 92*x^26 + 47*x^25 + 50*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 38*x^20 + 61*x^19 + 68*x^18 + 91*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 39*x^11 + 116*x^10 + 113*x^9 + 62*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 90*x^4 + 27*x^3 + 44*x^2 + 45*x + 126, x^95 + 15*x^93 + 126*x^92 + 53*x^91 + 28*x^90 + 115*x^89 + 106*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 30*x^84 + 9*x^83 + 68*x^82 + 111*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 115*x^75 + 20*x^74 + 69*x^73 + 86*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 18*x^68 + 119*x^67 + 76*x^66 + 49*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 105*x^27 + 76*x^26 + 95*x^25 + 18*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 86*x^20 + 109*x^19 + 20*x^18 + 107*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 87*x^11 + 68*x^10 + x^9 + 30*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 106*x^4 + 43*x^3 + 28*x^2 + 93*x + 126, x^95 + 15*x^93 + 50*x^92 + 5*x^91 + 20*x^90 + 99*x^89 + 86*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 50*x^84 + 121*x^83 + 76*x^82 + 63*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 99*x^75 + 124*x^74 + 21*x^73 + 42*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 94*x^68 + 71*x^67 + 100*x^66 + 33*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 121*x^27 + 36*x^26 + 15*x^25 + 46*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 58*x^20 + 29*x^19 + 60*x^18 + 123*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 7*x^11 + 12*x^10 + 17*x^9 + 98*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 70*x^4 + 59*x^3 + 84*x^2 + 13*x + 34, x^95 + 15*x^93 + 78*x^92 + 37*x^91 + 12*x^90 + 67*x^89 + 10*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 14*x^84 + 89*x^83 + 20*x^82 + 95*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 67*x^75 + 100*x^74 + 53*x^73 + 118*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 98*x^68 + 103*x^67 + 60*x^66 + x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 25*x^27 + 124*x^26 + 111*x^25 + 50*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 6*x^20 + 125*x^19 + 36*x^18 + 27*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 103*x^11 + 84*x^10 + 49*x^9 + 62*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 122*x^4 + 91*x^3 + 76*x^2 + 109*x + 62, x^95 + 15*x^93 + 110*x^92 + 21*x^91 + 60*x^90 + 83*x^89 + 58*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 14*x^84 + 41*x^83 + 36*x^82 + 15*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 19*x^75 + 116*x^74 + 101*x^73 + 6*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 34*x^68 + 87*x^67 + 108*x^66 + 17*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 73*x^27 + 108*x^26 + 63*x^25 + 34*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 6*x^20 + 13*x^19 + 116*x^18 + 11*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 119*x^11 + 36*x^10 + 33*x^9 + 14*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 58*x^4 + 11*x^3 + 60*x^2 + 61*x + 110, x^95 + 15*x^93 + 6*x^92 + 117*x^91 + 124*x^90 + 19*x^89 + 18*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 6*x^84 + 73*x^83 + 36*x^82 + 79*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 51*x^75 + 52*x^74 + 37*x^73 + 110*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 42*x^68 + 55*x^67 + 108*x^66 + 81*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 41*x^27 + 44*x^26 + 127*x^25 + 90*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 94*x^20 + 45*x^19 + 116*x^18 + 75*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 23*x^11 + 100*x^10 + 97*x^9 + 86*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 34*x^4 + 107*x^3 + 60*x^2 + 125*x + 22, x^95 + 15*x^93 + 62*x^92 + 37*x^91 + 76*x^90 + 67*x^89 + 122*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 62*x^84 + 89*x^83 + 84*x^82 + 95*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 67*x^75 + 36*x^74 + 53*x^73 + 6*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 50*x^68 + 103*x^67 + 124*x^66 + x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 25*x^27 + 60*x^26 + 111*x^25 + 98*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 118*x^20 + 125*x^19 + 100*x^18 + 27*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 103*x^11 + 20*x^10 + 49*x^9 + 14*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 10*x^4 + 91*x^3 + 12*x^2 + 109*x + 78, x^95 + 15*x^93 + 118*x^92 + 21*x^91 + 28*x^90 + 115*x^89 + 34*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 118*x^84 + 41*x^83 + 4*x^82 + 111*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 19*x^75 + 20*x^74 + 69*x^73 + 94*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 58*x^68 + 87*x^67 + 12*x^66 + 49*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 73*x^27 + 76*x^26 + 95*x^25 + 42*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 14*x^20 + 13*x^19 + 84*x^18 + 107*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 119*x^11 + 68*x^10 + x^9 + 6*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 114*x^4 + 11*x^3 + 92*x^2 + 93*x + 70, x^95 + 15*x^93 + 122*x^92 + 21*x^91 + 36*x^90 + 115*x^89 + 78*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 58*x^84 + 41*x^83 + 60*x^82 + 111*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 19*x^75 + 44*x^74 + 69*x^73 + 50*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 22*x^68 + 87*x^67 + 52*x^66 + 49*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 73*x^27 + 116*x^26 + 95*x^25 + 6*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 98*x^20 + 13*x^19 + 108*x^18 + 107*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 119*x^11 + 124*x^10 + x^9 + 74*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 30*x^4 + 11*x^3 + 100*x^2 + 93*x + 74, x^95 + 15*x^93 + 30*x^92 + 85*x^91 + 28*x^90 + 19*x^89 + 74*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 62*x^84 + 105*x^83 + 68*x^82 + 79*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 83*x^75 + 20*x^74 + 37*x^73 + 118*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 114*x^68 + 23*x^67 + 76*x^66 + 81*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 9*x^27 + 76*x^26 + 127*x^25 + 114*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 118*x^20 + 77*x^19 + 20*x^18 + 75*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 55*x^11 + 68*x^10 + 97*x^9 + 62*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 74*x^4 + 75*x^3 + 28*x^2 + 125*x + 30, x^95 + 15*x^93 + 50*x^92 + 69*x^91 + 52*x^90 + 35*x^89 + 54*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 114*x^84 + 57*x^83 + 44*x^82 + 127*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 35*x^75 + 92*x^74 + 85*x^73 + 74*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 30*x^68 + 7*x^67 + 4*x^66 + 97*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 57*x^27 + 68*x^26 + 79*x^25 + 14*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 122*x^20 + 93*x^19 + 28*x^18 + 59*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 71*x^11 + 108*x^10 + 81*x^9 + 2*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 6*x^4 + 123*x^3 + 116*x^2 + 77*x + 2, x^95 + 15*x^93 + 78*x^92 + 21*x^91 + 60*x^90 + 83*x^89 + 26*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 110*x^84 + 41*x^83 + 36*x^82 + 15*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 19*x^75 + 116*x^74 + 101*x^73 + 38*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 66*x^68 + 87*x^67 + 108*x^66 + 17*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 73*x^27 + 108*x^26 + 63*x^25 + 2*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 102*x^20 + 13*x^19 + 116*x^18 + 11*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 119*x^11 + 36*x^10 + 33*x^9 + 46*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 90*x^4 + 11*x^3 + 60*x^2 + 61*x + 14, x^95 + 15*x^93 + 42*x^92 + 85*x^91 + 4*x^90 + 115*x^89 + 30*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 106*x^84 + 105*x^83 + 92*x^82 + 111*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 83*x^75 + 76*x^74 + 69*x^73 + 98*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 102*x^68 + 23*x^67 + 20*x^66 + 49*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 9*x^27 + 84*x^26 + 95*x^25 + 22*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 82*x^20 + 77*x^19 + 12*x^18 + 107*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 55*x^11 + 28*x^10 + x^9 + 58*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 46*x^4 + 75*x^3 + 68*x^2 + 93*x + 58, x^95 + 15*x^93 + 38*x^92 + 85*x^91 + 28*x^90 + 51*x^89 + 18*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 102*x^84 + 105*x^83 + 4*x^82 + 47*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 83*x^75 + 20*x^74 + 5*x^73 + 110*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 74*x^68 + 23*x^67 + 12*x^66 + 113*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 9*x^27 + 76*x^26 + 31*x^25 + 90*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 62*x^20 + 77*x^19 + 84*x^18 + 43*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 55*x^11 + 68*x^10 + 65*x^9 + 86*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 66*x^4 + 75*x^3 + 92*x^2 + 29*x + 86, x^95 + 15*x^93 + 62*x^92 + 69*x^91 + 76*x^90 + 99*x^89 + 58*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 62*x^84 + 57*x^83 + 84*x^82 + 63*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 35*x^75 + 36*x^74 + 21*x^73 + 70*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 50*x^68 + 7*x^67 + 124*x^66 + 33*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 57*x^27 + 60*x^26 + 15*x^25 + 34*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 118*x^20 + 93*x^19 + 100*x^18 + 123*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 71*x^11 + 20*x^10 + 17*x^9 + 78*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 10*x^4 + 123*x^3 + 12*x^2 + 13*x + 14, x^95 + 15*x^93 + 46*x^92 + 53*x^91 + 92*x^90 + 115*x^89 + 26*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 14*x^84 + 9*x^83 + 4*x^82 + 111*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 115*x^75 + 84*x^74 + 69*x^73 + 38*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 34*x^68 + 119*x^67 + 12*x^66 + 49*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 105*x^27 + 12*x^26 + 95*x^25 + 2*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 6*x^20 + 109*x^19 + 84*x^18 + 107*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 87*x^11 + 4*x^10 + x^9 + 46*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 58*x^4 + 43*x^3 + 92*x^2 + 93*x + 78, x^95 + 15*x^93 + 42*x^92 + 101*x^91 + 52*x^90 + 35*x^89 + 110*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 74*x^84 + 25*x^83 + 108*x^82 + 127*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 3*x^75 + 92*x^74 + 85*x^73 + 82*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 70*x^68 + 39*x^67 + 68*x^66 + 97*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 89*x^27 + 68*x^26 + 79*x^25 + 38*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 50*x^20 + 61*x^19 + 92*x^18 + 59*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 39*x^11 + 108*x^10 + 81*x^9 + 106*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 14*x^4 + 27*x^3 + 52*x^2 + 77*x + 74, x^95 + 15*x^93 + 126*x^92 + 117*x^91 + 124*x^90 + 51*x^89 + 10*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 94*x^84 + 73*x^83 + 100*x^82 + 47*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 51*x^75 + 52*x^74 + 5*x^73 + 54*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 82*x^68 + 55*x^67 + 44*x^66 + 113*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 41*x^27 + 44*x^26 + 31*x^25 + 50*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 22*x^20 + 45*x^19 + 52*x^18 + 43*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 23*x^11 + 100*x^10 + 65*x^9 + 126*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 42*x^4 + 107*x^3 + 124*x^2 + 29*x + 30, x^95 + 15*x^93 + 50*x^92 + 37*x^91 + 116*x^90 + 3*x^89 + 54*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 114*x^84 + 89*x^83 + 108*x^82 + 31*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 67*x^75 + 28*x^74 + 117*x^73 + 74*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 30*x^68 + 103*x^67 + 68*x^66 + 65*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 25*x^27 + 4*x^26 + 47*x^25 + 14*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 122*x^20 + 125*x^19 + 92*x^18 + 91*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 103*x^11 + 44*x^10 + 113*x^9 + 2*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 6*x^4 + 91*x^3 + 52*x^2 + 45*x + 2, x^95 + 15*x^93 + 82*x^92 + 37*x^91 + 116*x^90 + 67*x^89 + 22*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 18*x^84 + 89*x^83 + 108*x^82 + 95*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 67*x^75 + 28*x^74 + 53*x^73 + 106*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 126*x^68 + 103*x^67 + 68*x^66 + x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 25*x^27 + 4*x^26 + 111*x^25 + 110*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 26*x^20 + 125*x^19 + 92*x^18 + 27*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 103*x^11 + 44*x^10 + 49*x^9 + 34*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 102*x^4 + 91*x^3 + 52*x^2 + 109*x + 34, x^95 + 15*x^93 + 86*x^92 + 85*x^91 + 124*x^90 + 115*x^89 + 98*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 22*x^84 + 105*x^83 + 36*x^82 + 111*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 83*x^75 + 52*x^74 + 69*x^73 + 30*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 26*x^68 + 23*x^67 + 108*x^66 + 49*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 9*x^27 + 44*x^26 + 95*x^25 + 106*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 46*x^20 + 77*x^19 + 116*x^18 + 107*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 55*x^11 + 100*x^10 + x^9 + 70*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 82*x^4 + 75*x^3 + 60*x^2 + 93*x + 70, x^95 + 15*x^93 + 122*x^92 + 85*x^91 + 4*x^90 + 115*x^89 + 46*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 122*x^84 + 105*x^83 + 92*x^82 + 111*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 83*x^75 + 76*x^74 + 69*x^73 + 82*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 86*x^68 + 23*x^67 + 20*x^66 + 49*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 9*x^27 + 84*x^26 + 95*x^25 + 102*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 34*x^20 + 77*x^19 + 12*x^18 + 107*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 55*x^11 + 28*x^10 + x^9 + 106*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 94*x^4 + 75*x^3 + 68*x^2 + 93*x + 42, x^95 + 15*x^93 + 46*x^92 + 37*x^91 + 44*x^90 + 67*x^89 + 74*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 46*x^84 + 89*x^83 + 116*x^82 + 95*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 67*x^75 + 68*x^74 + 53*x^73 + 54*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 66*x^68 + 103*x^67 + 92*x^66 + x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 25*x^27 + 28*x^26 + 111*x^25 + 114*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 38*x^20 + 125*x^19 + 4*x^18 + 27*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 103*x^11 + 52*x^10 + 49*x^9 + 126*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 90*x^4 + 91*x^3 + 108*x^2 + 109*x + 62, x^95 + 15*x^93 + 42*x^92 + 21*x^91 + 36*x^90 + 115*x^89 + 62*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 42*x^84 + 41*x^83 + 60*x^82 + 111*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 19*x^75 + 44*x^74 + 69*x^73 + 66*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 38*x^68 + 87*x^67 + 52*x^66 + 49*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 73*x^27 + 116*x^26 + 95*x^25 + 54*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 18*x^20 + 13*x^19 + 108*x^18 + 107*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 119*x^11 + 124*x^10 + x^9 + 26*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 110*x^4 + 11*x^3 + 100*x^2 + 93*x + 90, x^95 + 15*x^93 + 34*x^92 + 101*x^91 + 20*x^90 + 67*x^89 + 70*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 98*x^84 + 25*x^83 + 76*x^82 + 95*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 3*x^75 + 124*x^74 + 53*x^73 + 58*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 46*x^68 + 39*x^67 + 100*x^66 + x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 89*x^27 + 36*x^26 + 111*x^25 + 94*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 42*x^20 + 61*x^19 + 60*x^18 + 27*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 39*x^11 + 12*x^10 + 49*x^9 + 50*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 86*x^4 + 27*x^3 + 84*x^2 + 109*x + 50, x^95 + 15*x^93 + 38*x^92 + 85*x^91 + 60*x^90 + 51*x^89 + 114*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 38*x^84 + 105*x^83 + 100*x^82 + 47*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 83*x^75 + 116*x^74 + 5*x^73 + 14*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 10*x^68 + 23*x^67 + 44*x^66 + 113*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 9*x^27 + 108*x^26 + 31*x^25 + 58*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 126*x^20 + 77*x^19 + 52*x^18 + 43*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 55*x^11 + 36*x^10 + 65*x^9 + 118*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 2*x^4 + 75*x^3 + 124*x^2 + 29*x + 54, x^95 + 15*x^93 + 26*x^92 + 101*x^91 + 20*x^90 + 99*x^89 + 126*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 58*x^84 + 25*x^83 + 12*x^82 + 63*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 3*x^75 + 124*x^74 + 21*x^73 + 66*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 86*x^68 + 39*x^67 + 36*x^66 + 33*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 89*x^27 + 36*x^26 + 15*x^25 + 118*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 98*x^20 + 61*x^19 + 124*x^18 + 123*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 39*x^11 + 12*x^10 + 17*x^9 + 26*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 94*x^4 + 27*x^3 + 20*x^2 + 13*x + 122, x^95 + 15*x^93 + 42*x^92 + 117*x^91 + 4*x^90 + 19*x^89 + 94*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 106*x^84 + 73*x^83 + 92*x^82 + 79*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 51*x^75 + 76*x^74 + 37*x^73 + 34*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 102*x^68 + 55*x^67 + 20*x^66 + 81*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 41*x^27 + 84*x^26 + 127*x^25 + 86*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 82*x^20 + 45*x^19 + 12*x^18 + 75*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 23*x^11 + 28*x^10 + 97*x^9 + 122*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 46*x^4 + 107*x^3 + 68*x^2 + 125*x + 122, x^95 + 15*x^93 + 58*x^92 + 53*x^91 + 100*x^90 + 83*x^89 + 78*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 122*x^84 + 9*x^83 + 124*x^82 + 15*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 115*x^75 + 108*x^74 + 101*x^73 + 50*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 86*x^68 + 119*x^67 + 116*x^66 + 17*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 105*x^27 + 52*x^26 + 63*x^25 + 6*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 34*x^20 + 109*x^19 + 44*x^18 + 11*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 87*x^11 + 60*x^10 + 33*x^9 + 74*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 94*x^4 + 43*x^3 + 36*x^2 + 61*x + 74, x^95 + 15*x^93 + 14*x^92 + 21*x^91 + 124*x^90 + 83*x^89 + 26*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 46*x^84 + 41*x^83 + 100*x^82 + 15*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 19*x^75 + 52*x^74 + 101*x^73 + 38*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 2*x^68 + 87*x^67 + 44*x^66 + 17*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 73*x^27 + 44*x^26 + 63*x^25 + 2*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 38*x^20 + 13*x^19 + 52*x^18 + 11*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 119*x^11 + 100*x^10 + 33*x^9 + 46*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 26*x^4 + 11*x^3 + 124*x^2 + 61*x + 14, x^95 + 15*x^93 + 38*x^92 + 117*x^91 + 60*x^90 + 83*x^89 + 50*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 38*x^84 + 73*x^83 + 100*x^82 + 15*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 51*x^75 + 116*x^74 + 101*x^73 + 78*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 10*x^68 + 55*x^67 + 44*x^66 + 17*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 41*x^27 + 108*x^26 + 63*x^25 + 122*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 126*x^20 + 45*x^19 + 52*x^18 + 11*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 23*x^11 + 36*x^10 + 33*x^9 + 54*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 2*x^4 + 107*x^3 + 124*x^2 + 61*x + 118, x^95 + 15*x^93 + 62*x^92 + 53*x^91 + 28*x^90 + 115*x^89 + 42*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 94*x^84 + 9*x^83 + 68*x^82 + 111*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 115*x^75 + 20*x^74 + 69*x^73 + 22*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 82*x^68 + 119*x^67 + 76*x^66 + 49*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 105*x^27 + 76*x^26 + 95*x^25 + 82*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 22*x^20 + 109*x^19 + 20*x^18 + 107*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 87*x^11 + 68*x^10 + x^9 + 94*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 42*x^4 + 43*x^3 + 28*x^2 + 93*x + 62, x^95 + 15*x^93 + 62*x^92 + 21*x^91 + 60*x^90 + 83*x^89 + 74*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 30*x^84 + 41*x^83 + 36*x^82 + 15*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 19*x^75 + 116*x^74 + 101*x^73 + 118*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 18*x^68 + 87*x^67 + 108*x^66 + 17*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 73*x^27 + 108*x^26 + 63*x^25 + 114*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 86*x^20 + 13*x^19 + 116*x^18 + 11*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 119*x^11 + 36*x^10 + 33*x^9 + 62*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 106*x^4 + 11*x^3 + 60*x^2 + 61*x + 94, x^95 + 15*x^93 + 54*x^92 + 53*x^91 + 124*x^90 + 83*x^89 + 2*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 118*x^84 + 9*x^83 + 36*x^82 + 15*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 115*x^75 + 52*x^74 + 101*x^73 + 126*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 58*x^68 + 119*x^67 + 108*x^66 + 17*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 105*x^27 + 44*x^26 + 63*x^25 + 10*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 14*x^20 + 109*x^19 + 116*x^18 + 11*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 87*x^11 + 100*x^10 + 33*x^9 + 38*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 114*x^4 + 43*x^3 + 60*x^2 + 61*x + 38, x^95 + 15*x^93 + 66*x^92 + 85*x^91 + 100*x^90 + 19*x^89 + 22*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 34*x^84 + 105*x^83 + 60*x^82 + 79*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 83*x^75 + 108*x^74 + 37*x^73 + 42*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 46*x^68 + 23*x^67 + 52*x^66 + 81*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 9*x^27 + 52*x^26 + 127*x^25 + 110*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 106*x^20 + 77*x^19 + 108*x^18 + 75*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 55*x^11 + 60*x^10 + 97*x^9 + 98*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 86*x^4 + 75*x^3 + 100*x^2 + 125*x + 2, x^95 + 15*x^93 + 54*x^92 + 101*x^91 + 12*x^90 + 99*x^89 + 114*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 22*x^84 + 25*x^83 + 84*x^82 + 63*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 3*x^75 + 100*x^74 + 21*x^73 + 78*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 90*x^68 + 39*x^67 + 124*x^66 + 33*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 89*x^27 + 124*x^26 + 15*x^25 + 58*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 46*x^20 + 61*x^19 + 100*x^18 + 123*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 39*x^11 + 84*x^10 + 17*x^9 + 54*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 18*x^4 + 27*x^3 + 12*x^2 + 13*x + 86, x^95 + 15*x^93 + 6*x^92 + 37*x^91 + 108*x^90 + 35*x^89 + 34*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 102*x^84 + 89*x^83 + 116*x^82 + 127*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 67*x^75 + 4*x^74 + 85*x^73 + 30*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 10*x^68 + 103*x^67 + 92*x^66 + 97*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 25*x^27 + 92*x^26 + 79*x^25 + 42*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 62*x^20 + 125*x^19 + 4*x^18 + 59*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 103*x^11 + 116*x^10 + 81*x^9 + 70*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 2*x^4 + 91*x^3 + 108*x^2 + 77*x + 102, x^95 + 15*x^93 + 30*x^92 + 21*x^91 + 124*x^90 + 83*x^89 + 106*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 126*x^84 + 41*x^83 + 100*x^82 + 15*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 19*x^75 + 52*x^74 + 101*x^73 + 86*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 50*x^68 + 87*x^67 + 44*x^66 + 17*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 73*x^27 + 44*x^26 + 63*x^25 + 18*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 54*x^20 + 13*x^19 + 52*x^18 + 11*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 119*x^11 + 100*x^10 + 33*x^9 + 30*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 10*x^4 + 11*x^3 + 124*x^2 + 61*x + 62, x^95 + 15*x^93 + 74*x^92 + 101*x^91 + 116*x^90 + 99*x^89 + 14*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 106*x^84 + 25*x^83 + 44*x^82 + 63*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 3*x^75 + 28*x^74 + 21*x^73 + 50*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 38*x^68 + 39*x^67 + 4*x^66 + 33*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 89*x^27 + 4*x^26 + 15*x^25 + 70*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 82*x^20 + 61*x^19 + 28*x^18 + 123*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 39*x^11 + 44*x^10 + 17*x^9 + 74*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 110*x^4 + 27*x^3 + 116*x^2 + 13*x + 42, x^95 + 15*x^93 + 66*x^92 + 37*x^91 + 116*x^90 + 67*x^89 + 70*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 66*x^84 + 89*x^83 + 108*x^82 + 95*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 67*x^75 + 28*x^74 + 53*x^73 + 58*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 78*x^68 + 103*x^67 + 68*x^66 + x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 25*x^27 + 4*x^26 + 111*x^25 + 94*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 10*x^20 + 125*x^19 + 92*x^18 + 27*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 103*x^11 + 44*x^10 + 49*x^9 + 50*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 118*x^4 + 91*x^3 + 52*x^2 + 109*x + 114, x^95 + 15*x^93 + 18*x^92 + 5*x^91 + 20*x^90 + 99*x^89 + 54*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 18*x^84 + 121*x^83 + 76*x^82 + 63*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 99*x^75 + 124*x^74 + 21*x^73 + 74*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 126*x^68 + 71*x^67 + 100*x^66 + 33*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 121*x^27 + 36*x^26 + 15*x^25 + 14*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 26*x^20 + 29*x^19 + 60*x^18 + 123*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 7*x^11 + 12*x^10 + 17*x^9 + 2*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 102*x^4 + 59*x^3 + 84*x^2 + 13*x + 66, x^95 + 15*x^93 + 78*x^92 + 53*x^91 + 124*x^90 + 51*x^89 + 90*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 110*x^84 + 9*x^83 + 100*x^82 + 47*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 115*x^75 + 52*x^74 + 5*x^73 + 102*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 66*x^68 + 119*x^67 + 44*x^66 + 113*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 105*x^27 + 44*x^26 + 31*x^25 + 66*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 102*x^20 + 109*x^19 + 52*x^18 + 43*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 87*x^11 + 100*x^10 + 65*x^9 + 110*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 90*x^4 + 43*x^3 + 124*x^2 + 29*x + 78, x^95 + 15*x^93 + 38*x^92 + 37*x^91 + 108*x^90 + 35*x^89 + 66*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 6*x^84 + 89*x^83 + 116*x^82 + 127*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 67*x^75 + 4*x^74 + 85*x^73 + 126*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 106*x^68 + 103*x^67 + 92*x^66 + 97*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 25*x^27 + 92*x^26 + 79*x^25 + 74*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 94*x^20 + 125*x^19 + 4*x^18 + 59*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 103*x^11 + 116*x^10 + 81*x^9 + 38*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 98*x^4 + 91*x^3 + 108*x^2 + 77*x + 70, x^95 + 15*x^93 + 102*x^92 + 85*x^91 + 92*x^90 + 115*x^89 + 82*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 38*x^84 + 105*x^83 + 68*x^82 + 111*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 83*x^75 + 84*x^74 + 69*x^73 + 46*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 10*x^68 + 23*x^67 + 76*x^66 + 49*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 9*x^27 + 12*x^26 + 95*x^25 + 26*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 126*x^20 + 77*x^19 + 20*x^18 + 107*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 55*x^11 + 4*x^10 + x^9 + 22*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 2*x^4 + 75*x^3 + 28*x^2 + 93*x + 22, x^95 + 15*x^93 + 54*x^92 + 21*x^91 + 92*x^90 + 51*x^89 + 98*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 54*x^84 + 41*x^83 + 68*x^82 + 47*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 19*x^75 + 84*x^74 + 5*x^73 + 30*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 122*x^68 + 87*x^67 + 76*x^66 + 113*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 73*x^27 + 12*x^26 + 31*x^25 + 106*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 78*x^20 + 13*x^19 + 20*x^18 + 43*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 119*x^11 + 4*x^10 + 65*x^9 + 70*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 50*x^4 + 11*x^3 + 28*x^2 + 29*x + 6, x^95 + 15*x^93 + 90*x^92 + 37*x^91 + 116*x^90 + 35*x^89 + 94*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 58*x^84 + 89*x^83 + 44*x^82 + 127*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 67*x^75 + 28*x^74 + 85*x^73 + 98*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 86*x^68 + 103*x^67 + 4*x^66 + 97*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 25*x^27 + 4*x^26 + 79*x^25 + 86*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 98*x^20 + 125*x^19 + 28*x^18 + 59*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 103*x^11 + 44*x^10 + 81*x^9 + 58*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 94*x^4 + 91*x^3 + 116*x^2 + 77*x + 90, x^95 + 15*x^93 + 122*x^92 + 101*x^91 + 116*x^90 + 99*x^89 + 126*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 90*x^84 + 25*x^83 + 44*x^82 + 63*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 3*x^75 + 28*x^74 + 21*x^73 + 66*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 54*x^68 + 39*x^67 + 4*x^66 + 33*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 89*x^27 + 4*x^26 + 15*x^25 + 118*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 2*x^20 + 61*x^19 + 28*x^18 + 123*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 39*x^11 + 44*x^10 + 17*x^9 + 26*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 62*x^4 + 27*x^3 + 116*x^2 + 13*x + 58, x^95 + 15*x^93 + 58*x^92 + 21*x^91 + 100*x^90 + 51*x^89 + 14*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 122*x^84 + 41*x^83 + 124*x^82 + 47*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 19*x^75 + 108*x^74 + 5*x^73 + 114*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 86*x^68 + 87*x^67 + 116*x^66 + 113*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 73*x^27 + 52*x^26 + 31*x^25 + 70*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 34*x^20 + 13*x^19 + 44*x^18 + 43*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 119*x^11 + 60*x^10 + 65*x^9 + 10*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 94*x^4 + 11*x^3 + 36*x^2 + 29*x + 10, x^95 + 15*x^93 + 82*x^92 + 21*x^91 + 68*x^90 + 19*x^89 + 70*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 50*x^84 + 41*x^83 + 92*x^82 + 79*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 19*x^75 + 12*x^74 + 37*x^73 + 122*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 30*x^68 + 87*x^67 + 20*x^66 + 81*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 73*x^27 + 20*x^26 + 127*x^25 + 94*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 58*x^20 + 13*x^19 + 12*x^18 + 75*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 119*x^11 + 92*x^10 + 97*x^9 + 114*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 6*x^4 + 11*x^3 + 68*x^2 + 125*x + 18, x^95 + 15*x^93 + 126*x^92 + 21*x^91 + 28*x^90 + 83*x^89 + 42*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 30*x^84 + 41*x^83 + 68*x^82 + 15*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 19*x^75 + 20*x^74 + 101*x^73 + 22*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 18*x^68 + 87*x^67 + 76*x^66 + 17*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 73*x^27 + 76*x^26 + 63*x^25 + 82*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 86*x^20 + 13*x^19 + 20*x^18 + 11*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 119*x^11 + 68*x^10 + 33*x^9 + 94*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 106*x^4 + 11*x^3 + 28*x^2 + 61*x + 62, x^95 + 15*x^93 + 6*x^92 + 101*x^91 + 76*x^90 + 35*x^89 + 2*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 38*x^84 + 25*x^83 + 20*x^82 + 127*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 3*x^75 + 36*x^74 + 85*x^73 + 62*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 74*x^68 + 39*x^67 + 60*x^66 + 97*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 89*x^27 + 60*x^26 + 79*x^25 + 10*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 126*x^20 + 61*x^19 + 36*x^18 + 59*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 39*x^11 + 20*x^10 + 81*x^9 + 102*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 66*x^4 + 27*x^3 + 76*x^2 + 77*x + 70, x^95 + 15*x^93 + 2*x^92 + 117*x^91 + 4*x^90 + 115*x^89 + 54*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 34*x^84 + 73*x^83 + 28*x^82 + 111*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 51*x^75 + 76*x^74 + 69*x^73 + 10*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 46*x^68 + 55*x^67 + 84*x^66 + 49*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 41*x^27 + 84*x^26 + 95*x^25 + 14*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 106*x^20 + 45*x^19 + 76*x^18 + 107*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 23*x^11 + 28*x^10 + x^9 + 66*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 86*x^4 + 107*x^3 + 4*x^2 + 93*x + 34, x^95 + 15*x^93 + 14*x^92 + 37*x^91 + 12*x^90 + 67*x^89 + 74*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 78*x^84 + 89*x^83 + 20*x^82 + 95*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 67*x^75 + 100*x^74 + 53*x^73 + 54*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 34*x^68 + 103*x^67 + 60*x^66 + x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 25*x^27 + 124*x^26 + 111*x^25 + 114*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 70*x^20 + 125*x^19 + 36*x^18 + 27*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 103*x^11 + 84*x^10 + 49*x^9 + 126*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 58*x^4 + 91*x^3 + 76*x^2 + 109*x + 126, x^95 + 15*x^93 + 94*x^92 + 101*x^91 + 44*x^90 + 67*x^89 + 122*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 30*x^84 + 25*x^83 + 116*x^82 + 95*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 3*x^75 + 68*x^74 + 53*x^73 + 6*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 82*x^68 + 39*x^67 + 92*x^66 + x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 89*x^27 + 28*x^26 + 111*x^25 + 98*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 86*x^20 + 61*x^19 + 4*x^18 + 27*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 39*x^11 + 52*x^10 + 49*x^9 + 14*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 42*x^4 + 27*x^3 + 108*x^2 + 109*x + 14, x^95 + 15*x^93 + 66*x^92 + 69*x^91 + 116*x^90 + 99*x^89 + 6*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 66*x^84 + 57*x^83 + 108*x^82 + 63*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 35*x^75 + 28*x^74 + 21*x^73 + 122*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 78*x^68 + 7*x^67 + 68*x^66 + 33*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 57*x^27 + 4*x^26 + 15*x^25 + 30*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 10*x^20 + 93*x^19 + 92*x^18 + 123*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 71*x^11 + 44*x^10 + 17*x^9 + 114*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 118*x^4 + 123*x^3 + 52*x^2 + 13*x + 50, x^95 + 15*x^93 + 78*x^92 + 101*x^91 + 76*x^90 + 67*x^89 + 10*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 14*x^84 + 25*x^83 + 84*x^82 + 95*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 3*x^75 + 36*x^74 + 53*x^73 + 118*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 98*x^68 + 39*x^67 + 124*x^66 + x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 89*x^27 + 60*x^26 + 111*x^25 + 50*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 6*x^20 + 61*x^19 + 100*x^18 + 27*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 39*x^11 + 20*x^10 + 49*x^9 + 62*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 122*x^4 + 27*x^3 + 12*x^2 + 109*x + 62, x^95 + 15*x^93 + 66*x^92 + 85*x^91 + 4*x^90 + 83*x^89 + 54*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 98*x^84 + 105*x^83 + 28*x^82 + 15*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 83*x^75 + 76*x^74 + 101*x^73 + 10*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 110*x^68 + 23*x^67 + 84*x^66 + 17*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 9*x^27 + 84*x^26 + 63*x^25 + 14*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 42*x^20 + 77*x^19 + 76*x^18 + 11*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 55*x^11 + 28*x^10 + 33*x^9 + 66*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 22*x^4 + 75*x^3 + 4*x^2 + 61*x + 34, x^95 + 15*x^93 + 18*x^92 + 21*x^91 + 36*x^90 + 19*x^89 + 38*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 50*x^84 + 41*x^83 + 124*x^82 + 79*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 19*x^75 + 44*x^74 + 37*x^73 + 26*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 30*x^68 + 87*x^67 + 116*x^66 + 81*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 73*x^27 + 116*x^26 + 127*x^25 + 62*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 58*x^20 + 13*x^19 + 44*x^18 + 75*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 119*x^11 + 124*x^10 + 97*x^9 + 18*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 6*x^4 + 11*x^3 + 36*x^2 + 125*x + 114, x^95 + 15*x^93 + 94*x^92 + 21*x^91 + 60*x^90 + 19*x^89 + 42*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 62*x^84 + 41*x^83 + 36*x^82 + 79*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 19*x^75 + 116*x^74 + 37*x^73 + 22*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 114*x^68 + 87*x^67 + 108*x^66 + 81*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 73*x^27 + 108*x^26 + 127*x^25 + 82*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 118*x^20 + 13*x^19 + 116*x^18 + 75*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 119*x^11 + 36*x^10 + 97*x^9 + 94*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 74*x^4 + 11*x^3 + 60*x^2 + 125*x + 126, x^95 + 15*x^93 + 118*x^92 + 37*x^91 + 76*x^90 + 35*x^89 + 114*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 86*x^84 + 89*x^83 + 20*x^82 + 127*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 67*x^75 + 36*x^74 + 85*x^73 + 78*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 26*x^68 + 103*x^67 + 60*x^66 + 97*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 25*x^27 + 60*x^26 + 79*x^25 + 58*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 110*x^20 + 125*x^19 + 36*x^18 + 59*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 103*x^11 + 20*x^10 + 81*x^9 + 54*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 82*x^4 + 91*x^3 + 76*x^2 + 77*x + 86, x^95 + 15*x^93 + 98*x^92 + 53*x^91 + 100*x^90 + 115*x^89 + 118*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 66*x^84 + 9*x^83 + 60*x^82 + 111*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 115*x^75 + 108*x^74 + 69*x^73 + 74*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 14*x^68 + 119*x^67 + 52*x^66 + 49*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 105*x^27 + 52*x^26 + 95*x^25 + 78*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 10*x^20 + 109*x^19 + 108*x^18 + 107*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 87*x^11 + 60*x^10 + x^9 + 2*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 54*x^4 + 43*x^3 + 100*x^2 + 93*x + 34, x^95 + 15*x^93 + 30*x^92 + 53*x^91 + 124*x^90 + 115*x^89 + 42*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 126*x^84 + 9*x^83 + 100*x^82 + 111*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 115*x^75 + 52*x^74 + 69*x^73 + 22*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 50*x^68 + 119*x^67 + 44*x^66 + 49*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 105*x^27 + 44*x^26 + 95*x^25 + 82*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 54*x^20 + 109*x^19 + 52*x^18 + 107*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 87*x^11 + 100*x^10 + x^9 + 94*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 10*x^4 + 43*x^3 + 124*x^2 + 93*x + 126, x^95 + 15*x^93 + 114*x^92 + 5*x^91 + 20*x^90 + 35*x^89 + 86*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 114*x^84 + 121*x^83 + 76*x^82 + 127*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 99*x^75 + 124*x^74 + 85*x^73 + 42*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 30*x^68 + 71*x^67 + 100*x^66 + 97*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 121*x^27 + 36*x^26 + 79*x^25 + 46*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 122*x^20 + 29*x^19 + 60*x^18 + 59*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 7*x^11 + 12*x^10 + 81*x^9 + 98*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 6*x^4 + 59*x^3 + 84*x^2 + 77*x + 34, x^95 + 15*x^93 + 38*x^92 + 21*x^91 + 124*x^90 + 115*x^89 + 50*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 38*x^84 + 41*x^83 + 36*x^82 + 111*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 19*x^75 + 52*x^74 + 69*x^73 + 78*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 10*x^68 + 87*x^67 + 108*x^66 + 49*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 73*x^27 + 44*x^26 + 95*x^25 + 122*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 126*x^20 + 13*x^19 + 116*x^18 + 107*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 119*x^11 + 100*x^10 + x^9 + 54*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 2*x^4 + 11*x^3 + 60*x^2 + 93*x + 118, x^95 + 15*x^93 + 10*x^92 + 117*x^91 + 68*x^90 + 19*x^89 + 126*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 74*x^84 + 73*x^83 + 28*x^82 + 79*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 51*x^75 + 12*x^74 + 37*x^73 + 2*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 6*x^68 + 55*x^67 + 84*x^66 + 81*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 41*x^27 + 20*x^26 + 127*x^25 + 118*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 50*x^20 + 45*x^19 + 76*x^18 + 75*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 23*x^11 + 92*x^10 + 97*x^9 + 90*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 78*x^4 + 107*x^3 + 4*x^2 + 125*x + 90, x^95 + 15*x^93 + 38*x^92 + 37*x^91 + 76*x^90 + 35*x^89 + 98*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 70*x^84 + 89*x^83 + 20*x^82 + 127*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 67*x^75 + 36*x^74 + 85*x^73 + 94*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 42*x^68 + 103*x^67 + 60*x^66 + 97*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 25*x^27 + 60*x^26 + 79*x^25 + 106*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 30*x^20 + 125*x^19 + 36*x^18 + 59*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 103*x^11 + 20*x^10 + 81*x^9 + 6*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 34*x^4 + 91*x^3 + 76*x^2 + 77*x + 102, x^95 + 15*x^93 + 22*x^92 + 5*x^91 + 76*x^90 + 67*x^89 + 18*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 118*x^84 + 121*x^83 + 20*x^82 + 95*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 99*x^75 + 36*x^74 + 53*x^73 + 46*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 122*x^68 + 71*x^67 + 60*x^66 + x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 121*x^27 + 60*x^26 + 111*x^25 + 90*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 14*x^20 + 29*x^19 + 36*x^18 + 27*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 7*x^11 + 20*x^10 + 49*x^9 + 22*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 50*x^4 + 59*x^3 + 76*x^2 + 109*x + 54, x^95 + 15*x^93 + 2*x^92 + 101*x^91 + 116*x^90 + 67*x^89 + 70*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 2*x^84 + 25*x^83 + 108*x^82 + 95*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 3*x^75 + 28*x^74 + 53*x^73 + 58*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 14*x^68 + 39*x^67 + 68*x^66 + x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 89*x^27 + 4*x^26 + 111*x^25 + 94*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 74*x^20 + 61*x^19 + 92*x^18 + 27*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 39*x^11 + 44*x^10 + 49*x^9 + 50*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 54*x^4 + 27*x^3 + 52*x^2 + 109*x + 114, x^95 + 15*x^93 + 58*x^92 + 101*x^91 + 84*x^90 + 99*x^89 + 94*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 90*x^84 + 25*x^83 + 76*x^82 + 63*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 3*x^75 + 60*x^74 + 21*x^73 + 98*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 54*x^68 + 39*x^67 + 100*x^66 + 33*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 89*x^27 + 100*x^26 + 15*x^25 + 86*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 2*x^20 + 61*x^19 + 60*x^18 + 123*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 39*x^11 + 76*x^10 + 17*x^9 + 58*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 62*x^4 + 27*x^3 + 84*x^2 + 13*x + 26, x^95 + 15*x^93 + 38*x^92 + 69*x^91 + 76*x^90 + 67*x^89 + 34*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 70*x^84 + 57*x^83 + 20*x^82 + 95*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 35*x^75 + 36*x^74 + 53*x^73 + 30*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 42*x^68 + 7*x^67 + 60*x^66 + x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 57*x^27 + 60*x^26 + 111*x^25 + 42*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 30*x^20 + 93*x^19 + 36*x^18 + 27*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 71*x^11 + 20*x^10 + 49*x^9 + 70*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 34*x^4 + 123*x^3 + 76*x^2 + 109*x + 38, x^95 + 15*x^93 + 14*x^92 + 21*x^91 + 60*x^90 + 83*x^89 + 90*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 46*x^84 + 41*x^83 + 36*x^82 + 15*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 19*x^75 + 116*x^74 + 101*x^73 + 102*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 2*x^68 + 87*x^67 + 108*x^66 + 17*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 73*x^27 + 108*x^26 + 63*x^25 + 66*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 38*x^20 + 13*x^19 + 116*x^18 + 11*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 119*x^11 + 36*x^10 + 33*x^9 + 110*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 26*x^4 + 11*x^3 + 60*x^2 + 61*x + 78, x^95 + 15*x^93 + 18*x^92 + 69*x^91 + 84*x^90 + 35*x^89 + 118*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 18*x^84 + 57*x^83 + 12*x^82 + 127*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 35*x^75 + 60*x^74 + 85*x^73 + 10*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 126*x^68 + 7*x^67 + 36*x^66 + 97*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 57*x^27 + 100*x^26 + 79*x^25 + 78*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 26*x^20 + 93*x^19 + 124*x^18 + 59*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 71*x^11 + 76*x^10 + 81*x^9 + 66*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 102*x^4 + 123*x^3 + 20*x^2 + 77*x + 2, x^95 + 15*x^93 + 34*x^92 + 101*x^91 + 84*x^90 + 3*x^89 + 70*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 98*x^84 + 25*x^83 + 12*x^82 + 31*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 3*x^75 + 60*x^74 + 117*x^73 + 58*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 46*x^68 + 39*x^67 + 36*x^66 + 65*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 89*x^27 + 100*x^26 + 47*x^25 + 94*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 42*x^20 + 61*x^19 + 124*x^18 + 91*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 39*x^11 + 76*x^10 + 113*x^9 + 50*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 86*x^4 + 27*x^3 + 20*x^2 + 45*x + 50, x^95 + 15*x^93 + 10*x^92 + 85*x^91 + 100*x^90 + 51*x^89 + 94*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 10*x^84 + 105*x^83 + 124*x^82 + 47*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 83*x^75 + 108*x^74 + 5*x^73 + 34*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 70*x^68 + 23*x^67 + 116*x^66 + 113*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 9*x^27 + 52*x^26 + 31*x^25 + 86*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 114*x^20 + 77*x^19 + 44*x^18 + 43*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 55*x^11 + 60*x^10 + 65*x^9 + 122*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 14*x^4 + 75*x^3 + 36*x^2 + 29*x + 58, x^95 + 15*x^93 + 50*x^92 + 117*x^91 + 100*x^90 + 51*x^89 + 6*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 82*x^84 + 73*x^83 + 60*x^82 + 47*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 51*x^75 + 108*x^74 + 5*x^73 + 58*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 126*x^68 + 55*x^67 + 52*x^66 + 113*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 41*x^27 + 52*x^26 + 31*x^25 + 30*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 90*x^20 + 45*x^19 + 108*x^18 + 43*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 23*x^11 + 60*x^10 + 65*x^9 + 50*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 102*x^4 + 107*x^3 + 100*x^2 + 29*x + 18, x^95 + 15*x^93 + 78*x^92 + 85*x^91 + 28*x^90 + 83*x^89 + 122*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 46*x^84 + 105*x^83 + 68*x^82 + 15*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 83*x^75 + 20*x^74 + 101*x^73 + 70*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 2*x^68 + 23*x^67 + 76*x^66 + 17*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 9*x^27 + 76*x^26 + 63*x^25 + 98*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 38*x^20 + 77*x^19 + 20*x^18 + 11*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 55*x^11 + 68*x^10 + 33*x^9 + 78*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 26*x^4 + 75*x^3 + 28*x^2 + 61*x + 110, x^95 + 15*x^93 + 66*x^92 + 21*x^91 + 4*x^90 + 19*x^89 + 54*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 98*x^84 + 41*x^83 + 28*x^82 + 79*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 19*x^75 + 76*x^74 + 37*x^73 + 10*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 110*x^68 + 87*x^67 + 84*x^66 + 81*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 73*x^27 + 84*x^26 + 127*x^25 + 14*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 42*x^20 + 13*x^19 + 76*x^18 + 75*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 119*x^11 + 28*x^10 + 97*x^9 + 66*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 22*x^4 + 11*x^3 + 4*x^2 + 125*x + 34, x^95 + 15*x^93 + 70*x^92 + 101*x^91 + 44*x^90 + 99*x^89 + 34*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 38*x^84 + 25*x^83 + 52*x^82 + 63*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 3*x^75 + 68*x^74 + 21*x^73 + 30*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 74*x^68 + 39*x^67 + 28*x^66 + 33*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 89*x^27 + 28*x^26 + 15*x^25 + 42*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 126*x^20 + 61*x^19 + 68*x^18 + 123*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 39*x^11 + 52*x^10 + 17*x^9 + 70*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 66*x^4 + 27*x^3 + 44*x^2 + 13*x + 102, x^95 + 15*x^93 + 50*x^92 + 69*x^91 + 84*x^90 + 99*x^89 + 86*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 50*x^84 + 57*x^83 + 12*x^82 + 63*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 35*x^75 + 60*x^74 + 21*x^73 + 42*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 94*x^68 + 7*x^67 + 36*x^66 + 33*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 57*x^27 + 100*x^26 + 15*x^25 + 46*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 58*x^20 + 93*x^19 + 124*x^18 + 123*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 71*x^11 + 76*x^10 + 17*x^9 + 98*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 70*x^4 + 123*x^3 + 20*x^2 + 13*x + 34, x^95 + 15*x^93 + 38*x^92 + 53*x^91 + 60*x^90 + 19*x^89 + 50*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 38*x^84 + 9*x^83 + 100*x^82 + 79*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 115*x^75 + 116*x^74 + 37*x^73 + 78*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 10*x^68 + 119*x^67 + 44*x^66 + 81*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 105*x^27 + 108*x^26 + 127*x^25 + 122*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 126*x^20 + 109*x^19 + 52*x^18 + 75*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 87*x^11 + 36*x^10 + 97*x^9 + 54*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 2*x^4 + 43*x^3 + 124*x^2 + 125*x + 118, x^95 + 15*x^93 + 58*x^92 + 5*x^91 + 52*x^90 + 67*x^89 + 126*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 26*x^84 + 121*x^83 + 108*x^82 + 95*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 99*x^75 + 92*x^74 + 53*x^73 + 66*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 118*x^68 + 71*x^67 + 68*x^66 + x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 121*x^27 + 68*x^26 + 111*x^25 + 118*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 66*x^20 + 29*x^19 + 92*x^18 + 27*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 7*x^11 + 108*x^10 + 49*x^9 + 26*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 126*x^4 + 59*x^3 + 52*x^2 + 109*x + 58, x^95 + 15*x^93 + 34*x^92 + 101*x^91 + 52*x^90 + 67*x^89 + 38*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 34*x^84 + 25*x^83 + 44*x^82 + 95*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 3*x^75 + 92*x^74 + 53*x^73 + 90*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 110*x^68 + 39*x^67 + 4*x^66 + x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 89*x^27 + 68*x^26 + 111*x^25 + 62*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 106*x^20 + 61*x^19 + 28*x^18 + 27*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 39*x^11 + 108*x^10 + 49*x^9 + 82*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 22*x^4 + 27*x^3 + 116*x^2 + 109*x + 18, x^95 + 15*x^93 + 30*x^92 + 21*x^91 + 92*x^90 + 83*x^89 + 10*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 62*x^84 + 41*x^83 + 4*x^82 + 15*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 19*x^75 + 84*x^74 + 101*x^73 + 54*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 114*x^68 + 87*x^67 + 12*x^66 + 17*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 73*x^27 + 12*x^26 + 63*x^25 + 50*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 118*x^20 + 13*x^19 + 84*x^18 + 11*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 119*x^11 + 4*x^10 + 33*x^9 + 126*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 74*x^4 + 11*x^3 + 92*x^2 + 61*x + 94, x^95 + 15*x^93 + 18*x^92 + 69*x^91 + 20*x^90 + 35*x^89 + 54*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 18*x^84 + 57*x^83 + 76*x^82 + 127*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 35*x^75 + 124*x^74 + 85*x^73 + 74*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 126*x^68 + 7*x^67 + 100*x^66 + 97*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 57*x^27 + 36*x^26 + 79*x^25 + 14*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 26*x^20 + 93*x^19 + 60*x^18 + 59*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 71*x^11 + 12*x^10 + 81*x^9 + 2*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 102*x^4 + 123*x^3 + 84*x^2 + 77*x + 66, x^95 + 15*x^93 + 98*x^92 + 117*x^91 + 4*x^90 + 51*x^89 + 86*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 2*x^84 + 73*x^83 + 28*x^82 + 47*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 51*x^75 + 76*x^74 + 5*x^73 + 106*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 78*x^68 + 55*x^67 + 84*x^66 + 113*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 41*x^27 + 84*x^26 + 31*x^25 + 46*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 74*x^20 + 45*x^19 + 76*x^18 + 43*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 23*x^11 + 28*x^10 + 65*x^9 + 34*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 118*x^4 + 107*x^3 + 4*x^2 + 29*x + 2, x^95 + 15*x^93 + 78*x^92 + 85*x^91 + 28*x^90 + 19*x^89 + 58*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 46*x^84 + 105*x^83 + 68*x^82 + 79*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 83*x^75 + 20*x^74 + 37*x^73 + 6*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 2*x^68 + 23*x^67 + 76*x^66 + 81*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 9*x^27 + 76*x^26 + 127*x^25 + 34*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 38*x^20 + 77*x^19 + 20*x^18 + 75*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 55*x^11 + 68*x^10 + 97*x^9 + 14*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 26*x^4 + 75*x^3 + 28*x^2 + 125*x + 46, x^95 + 15*x^93 + 122*x^92 + 85*x^91 + 4*x^90 + 51*x^89 + 110*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 122*x^84 + 105*x^83 + 92*x^82 + 47*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 83*x^75 + 76*x^74 + 5*x^73 + 18*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 86*x^68 + 23*x^67 + 20*x^66 + 113*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 9*x^27 + 84*x^26 + 31*x^25 + 38*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 34*x^20 + 77*x^19 + 12*x^18 + 43*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 55*x^11 + 28*x^10 + 65*x^9 + 42*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 94*x^4 + 75*x^3 + 68*x^2 + 29*x + 106, x^95 + 15*x^93 + 114*x^92 + 21*x^91 + 100*x^90 + 83*x^89 + 6*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 18*x^84 + 41*x^83 + 60*x^82 + 15*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 19*x^75 + 108*x^74 + 101*x^73 + 58*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 62*x^68 + 87*x^67 + 52*x^66 + 17*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 73*x^27 + 52*x^26 + 63*x^25 + 30*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 26*x^20 + 13*x^19 + 108*x^18 + 11*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 119*x^11 + 60*x^10 + 33*x^9 + 50*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 38*x^4 + 11*x^3 + 100*x^2 + 61*x + 18, x^95 + 15*x^93 + 70*x^92 + 37*x^91 + 76*x^90 + 35*x^89 + 2*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 102*x^84 + 89*x^83 + 20*x^82 + 127*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 67*x^75 + 36*x^74 + 85*x^73 + 62*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 10*x^68 + 103*x^67 + 60*x^66 + 97*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 25*x^27 + 60*x^26 + 79*x^25 + 10*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 62*x^20 + 125*x^19 + 36*x^18 + 59*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 103*x^11 + 20*x^10 + 81*x^9 + 102*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 2*x^4 + 91*x^3 + 76*x^2 + 77*x + 70, x^95 + 15*x^93 + 90*x^92 + 101*x^91 + 52*x^90 + 99*x^89 + 30*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 58*x^84 + 25*x^83 + 108*x^82 + 63*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 3*x^75 + 92*x^74 + 21*x^73 + 34*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 86*x^68 + 39*x^67 + 68*x^66 + 33*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 89*x^27 + 68*x^26 + 15*x^25 + 22*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 98*x^20 + 61*x^19 + 92*x^18 + 123*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 39*x^11 + 108*x^10 + 17*x^9 + 122*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 94*x^4 + 27*x^3 + 52*x^2 + 13*x + 26, x^95 + 15*x^93 + 34*x^92 + 85*x^91 + 4*x^90 + 83*x^89 + 22*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 66*x^84 + 105*x^83 + 28*x^82 + 15*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 83*x^75 + 76*x^74 + 101*x^73 + 42*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 14*x^68 + 23*x^67 + 84*x^66 + 17*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 9*x^27 + 84*x^26 + 63*x^25 + 110*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 10*x^20 + 77*x^19 + 76*x^18 + 11*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 55*x^11 + 28*x^10 + 33*x^9 + 98*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 54*x^4 + 75*x^3 + 4*x^2 + 61*x + 66, x^95 + 15*x^93 + 42*x^92 + 53*x^91 + 36*x^90 + 83*x^89 + 62*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 42*x^84 + 9*x^83 + 60*x^82 + 15*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 115*x^75 + 44*x^74 + 101*x^73 + 66*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 38*x^68 + 119*x^67 + 52*x^66 + 17*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 105*x^27 + 116*x^26 + 63*x^25 + 54*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 18*x^20 + 109*x^19 + 108*x^18 + 11*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 87*x^11 + 124*x^10 + 33*x^9 + 26*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 110*x^4 + 43*x^3 + 100*x^2 + 61*x + 90, x^95 + 15*x^93 + 118*x^92 + 101*x^91 + 44*x^90 + 35*x^89 + 82*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 22*x^84 + 25*x^83 + 52*x^82 + 127*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 3*x^75 + 68*x^74 + 85*x^73 + 110*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 90*x^68 + 39*x^67 + 28*x^66 + 97*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 89*x^27 + 28*x^26 + 79*x^25 + 26*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 46*x^20 + 61*x^19 + 68*x^18 + 59*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 39*x^11 + 52*x^10 + 81*x^9 + 86*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 18*x^4 + 27*x^3 + 44*x^2 + 77*x + 54, x^95 + 15*x^93 + 70*x^92 + 69*x^91 + 44*x^90 + 3*x^89 + 34*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 38*x^84 + 57*x^83 + 52*x^82 + 31*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 35*x^75 + 68*x^74 + 117*x^73 + 30*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 74*x^68 + 7*x^67 + 28*x^66 + 65*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 57*x^27 + 28*x^26 + 47*x^25 + 42*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 126*x^20 + 93*x^19 + 68*x^18 + 91*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 71*x^11 + 52*x^10 + 113*x^9 + 70*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 66*x^4 + 123*x^3 + 44*x^2 + 45*x + 102, x^95 + 15*x^93 + 22*x^92 + 117*x^91 + 28*x^90 + 83*x^89 + 2*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 22*x^84 + 73*x^83 + 4*x^82 + 15*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 51*x^75 + 20*x^74 + 101*x^73 + 126*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 26*x^68 + 55*x^67 + 12*x^66 + 17*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 41*x^27 + 76*x^26 + 63*x^25 + 10*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 46*x^20 + 45*x^19 + 84*x^18 + 11*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 23*x^11 + 68*x^10 + 33*x^9 + 38*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 82*x^4 + 107*x^3 + 92*x^2 + 61*x + 102, x^95 + 15*x^93 + 94*x^92 + 85*x^91 + 124*x^90 + 83*x^89 + 106*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 62*x^84 + 105*x^83 + 100*x^82 + 15*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 83*x^75 + 52*x^74 + 101*x^73 + 86*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 114*x^68 + 23*x^67 + 44*x^66 + 17*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 9*x^27 + 44*x^26 + 63*x^25 + 18*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 118*x^20 + 77*x^19 + 52*x^18 + 11*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 55*x^11 + 100*x^10 + 33*x^9 + 30*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 74*x^4 + 75*x^3 + 124*x^2 + 61*x + 62, x^95 + 15*x^93 + 102*x^92 + 101*x^91 + 76*x^90 + 99*x^89 + 34*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 6*x^84 + 25*x^83 + 20*x^82 + 63*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 3*x^75 + 36*x^74 + 21*x^73 + 30*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 106*x^68 + 39*x^67 + 60*x^66 + 33*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 89*x^27 + 60*x^26 + 15*x^25 + 42*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 94*x^20 + 61*x^19 + 36*x^18 + 123*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 39*x^11 + 20*x^10 + 17*x^9 + 70*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 98*x^4 + 27*x^3 + 76*x^2 + 13*x + 38, x^95 + 15*x^93 + 118*x^92 + 101*x^91 + 12*x^90 + 99*x^89 + 50*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 86*x^84 + 25*x^83 + 84*x^82 + 63*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 3*x^75 + 100*x^74 + 21*x^73 + 14*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 26*x^68 + 39*x^67 + 124*x^66 + 33*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 89*x^27 + 124*x^26 + 15*x^25 + 122*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 110*x^20 + 61*x^19 + 100*x^18 + 123*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 39*x^11 + 84*x^10 + 17*x^9 + 118*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 82*x^4 + 27*x^3 + 12*x^2 + 13*x + 22, x^95 + 15*x^93 + 14*x^92 + 37*x^91 + 76*x^90 + 3*x^89 + 74*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 78*x^84 + 89*x^83 + 84*x^82 + 31*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 67*x^75 + 36*x^74 + 117*x^73 + 54*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 34*x^68 + 103*x^67 + 124*x^66 + 65*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 25*x^27 + 60*x^26 + 47*x^25 + 114*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 70*x^20 + 125*x^19 + 100*x^18 + 91*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 103*x^11 + 20*x^10 + 113*x^9 + 126*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 58*x^4 + 91*x^3 + 12*x^2 + 45*x + 126, x^95 + 15*x^93 + 6*x^92 + 101*x^91 + 76*x^90 + 99*x^89 + 66*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 38*x^84 + 25*x^83 + 20*x^82 + 63*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 3*x^75 + 36*x^74 + 21*x^73 + 126*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 74*x^68 + 39*x^67 + 60*x^66 + 33*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 89*x^27 + 60*x^26 + 15*x^25 + 74*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 126*x^20 + 61*x^19 + 36*x^18 + 123*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 39*x^11 + 20*x^10 + 17*x^9 + 38*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 66*x^4 + 27*x^3 + 76*x^2 + 13*x + 6, x^95 + 15*x^93 + 10*x^92 + 117*x^91 + 36*x^90 + 83*x^89 + 94*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 10*x^84 + 73*x^83 + 60*x^82 + 15*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 51*x^75 + 44*x^74 + 101*x^73 + 34*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 70*x^68 + 55*x^67 + 52*x^66 + 17*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 41*x^27 + 116*x^26 + 63*x^25 + 86*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 114*x^20 + 45*x^19 + 108*x^18 + 11*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 23*x^11 + 124*x^10 + 33*x^9 + 122*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 14*x^4 + 107*x^3 + 100*x^2 + 61*x + 58, x^95 + 15*x^93 + 70*x^92 + 53*x^91 + 60*x^90 + 19*x^89 + 82*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 70*x^84 + 9*x^83 + 100*x^82 + 79*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 115*x^75 + 116*x^74 + 37*x^73 + 46*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 106*x^68 + 119*x^67 + 44*x^66 + 81*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 105*x^27 + 108*x^26 + 127*x^25 + 26*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 30*x^20 + 109*x^19 + 52*x^18 + 75*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 87*x^11 + 36*x^10 + 97*x^9 + 22*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 98*x^4 + 43*x^3 + 124*x^2 + 125*x + 86, x^95 + 15*x^93 + 126*x^92 + 69*x^91 + 108*x^90 + 99*x^89 + 90*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 62*x^84 + 57*x^83 + 52*x^82 + 63*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 35*x^75 + 4*x^74 + 21*x^73 + 38*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 50*x^68 + 7*x^67 + 28*x^66 + 33*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 57*x^27 + 92*x^26 + 15*x^25 + 66*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 118*x^20 + 93*x^19 + 68*x^18 + 123*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 71*x^11 + 116*x^10 + 17*x^9 + 46*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 10*x^4 + 123*x^3 + 44*x^2 + 13*x + 46, x^95 + 15*x^93 + 62*x^92 + 37*x^91 + 44*x^90 + 3*x^89 + 90*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 126*x^84 + 89*x^83 + 116*x^82 + 31*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 67*x^75 + 68*x^74 + 117*x^73 + 38*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 114*x^68 + 103*x^67 + 92*x^66 + 65*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 25*x^27 + 28*x^26 + 47*x^25 + 66*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 54*x^20 + 125*x^19 + 4*x^18 + 91*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 103*x^11 + 52*x^10 + 113*x^9 + 46*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 74*x^4 + 91*x^3 + 108*x^2 + 45*x + 46, x^95 + 15*x^93 + 58*x^92 + 53*x^91 + 36*x^90 + 19*x^89 + 78*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 122*x^84 + 9*x^83 + 60*x^82 + 79*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 115*x^75 + 44*x^74 + 37*x^73 + 50*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 86*x^68 + 119*x^67 + 52*x^66 + 81*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 105*x^27 + 116*x^26 + 127*x^25 + 6*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 34*x^20 + 109*x^19 + 108*x^18 + 75*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 87*x^11 + 124*x^10 + 97*x^9 + 74*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 94*x^4 + 43*x^3 + 100*x^2 + 125*x + 74, x^95 + 15*x^93 + 86*x^92 + 85*x^91 + 60*x^90 + 51*x^89 + 98*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 22*x^84 + 105*x^83 + 100*x^82 + 47*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 83*x^75 + 116*x^74 + 5*x^73 + 30*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 26*x^68 + 23*x^67 + 44*x^66 + 113*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 9*x^27 + 108*x^26 + 31*x^25 + 106*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 46*x^20 + 77*x^19 + 52*x^18 + 43*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 55*x^11 + 36*x^10 + 65*x^9 + 70*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 82*x^4 + 75*x^3 + 124*x^2 + 29*x + 70, x^95 + 15*x^93 + 94*x^92 + 69*x^91 + 44*x^90 + 99*x^89 + 122*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 30*x^84 + 57*x^83 + 116*x^82 + 63*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 35*x^75 + 68*x^74 + 21*x^73 + 6*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 82*x^68 + 7*x^67 + 92*x^66 + 33*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 57*x^27 + 28*x^26 + 15*x^25 + 98*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 86*x^20 + 93*x^19 + 4*x^18 + 123*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 71*x^11 + 52*x^10 + 17*x^9 + 14*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 42*x^4 + 123*x^3 + 108*x^2 + 13*x + 14, x^95 + 15*x^93 + 118*x^92 + 5*x^91 + 108*x^90 + 3*x^89 + 18*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 22*x^84 + 121*x^83 + 116*x^82 + 31*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 99*x^75 + 4*x^74 + 117*x^73 + 46*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 90*x^68 + 71*x^67 + 92*x^66 + 65*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 121*x^27 + 92*x^26 + 47*x^25 + 90*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 46*x^20 + 29*x^19 + 4*x^18 + 91*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 7*x^11 + 116*x^10 + 113*x^9 + 22*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 18*x^4 + 59*x^3 + 108*x^2 + 45*x + 118, x^95 + 15*x^93 + 78*x^92 + 85*x^91 + 60*x^90 + 83*x^89 + 90*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 110*x^84 + 105*x^83 + 36*x^82 + 15*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 83*x^75 + 116*x^74 + 101*x^73 + 102*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 66*x^68 + 23*x^67 + 108*x^66 + 17*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 9*x^27 + 108*x^26 + 63*x^25 + 66*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 102*x^20 + 77*x^19 + 116*x^18 + 11*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 55*x^11 + 36*x^10 + 33*x^9 + 110*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 90*x^4 + 75*x^3 + 60*x^2 + 61*x + 78, x^95 + 15*x^93 + 86*x^92 + 53*x^91 + 92*x^90 + 19*x^89 + 2*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 86*x^84 + 9*x^83 + 68*x^82 + 79*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 115*x^75 + 84*x^74 + 37*x^73 + 126*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 90*x^68 + 119*x^67 + 76*x^66 + 81*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 105*x^27 + 12*x^26 + 127*x^25 + 10*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 110*x^20 + 109*x^19 + 20*x^18 + 75*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 87*x^11 + 4*x^10 + 97*x^9 + 38*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 18*x^4 + 43*x^3 + 28*x^2 + 125*x + 102, x^95 + 15*x^93 + 34*x^92 + 21*x^91 + 4*x^90 + 19*x^89 + 22*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 66*x^84 + 41*x^83 + 28*x^82 + 79*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 19*x^75 + 76*x^74 + 37*x^73 + 42*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 14*x^68 + 87*x^67 + 84*x^66 + 81*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 73*x^27 + 84*x^26 + 127*x^25 + 110*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 10*x^20 + 13*x^19 + 76*x^18 + 75*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 119*x^11 + 28*x^10 + 97*x^9 + 98*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 54*x^4 + 11*x^3 + 4*x^2 + 125*x + 66, x^95 + 15*x^93 + 62*x^92 + 5*x^91 + 12*x^90 + 35*x^89 + 122*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 62*x^84 + 121*x^83 + 20*x^82 + 127*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 99*x^75 + 100*x^74 + 85*x^73 + 6*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 50*x^68 + 71*x^67 + 60*x^66 + 97*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 121*x^27 + 124*x^26 + 79*x^25 + 98*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 118*x^20 + 29*x^19 + 36*x^18 + 59*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 7*x^11 + 84*x^10 + 81*x^9 + 14*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 10*x^4 + 59*x^3 + 76*x^2 + 77*x + 78, x^95 + 15*x^93 + 54*x^92 + 69*x^91 + 44*x^90 + 3*x^89 + 82*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 86*x^84 + 57*x^83 + 52*x^82 + 31*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 35*x^75 + 68*x^74 + 117*x^73 + 110*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 26*x^68 + 7*x^67 + 28*x^66 + 65*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 57*x^27 + 28*x^26 + 47*x^25 + 26*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 110*x^20 + 93*x^19 + 68*x^18 + 91*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 71*x^11 + 52*x^10 + 113*x^9 + 86*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 82*x^4 + 123*x^3 + 44*x^2 + 45*x + 54, x^95 + 15*x^93 + 110*x^92 + 37*x^91 + 44*x^90 + 67*x^89 + 10*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 110*x^84 + 89*x^83 + 116*x^82 + 95*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 67*x^75 + 68*x^74 + 53*x^73 + 118*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 2*x^68 + 103*x^67 + 92*x^66 + x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 25*x^27 + 28*x^26 + 111*x^25 + 50*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 102*x^20 + 125*x^19 + 4*x^18 + 27*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 103*x^11 + 52*x^10 + 49*x^9 + 62*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 26*x^4 + 91*x^3 + 108*x^2 + 109*x + 126, x^95 + 15*x^93 + 78*x^92 + 5*x^91 + 44*x^90 + 99*x^89 + 106*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 78*x^84 + 121*x^83 + 116*x^82 + 63*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 99*x^75 + 68*x^74 + 21*x^73 + 22*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 34*x^68 + 71*x^67 + 92*x^66 + 33*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 121*x^27 + 28*x^26 + 15*x^25 + 18*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 70*x^20 + 29*x^19 + 4*x^18 + 123*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 7*x^11 + 52*x^10 + 17*x^9 + 94*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 58*x^4 + 59*x^3 + 108*x^2 + 13*x + 30, x^95 + 15*x^93 + 82*x^92 + 85*x^91 + 36*x^90 + 19*x^89 + 38*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 114*x^84 + 105*x^83 + 124*x^82 + 79*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 83*x^75 + 44*x^74 + 37*x^73 + 26*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 94*x^68 + 23*x^67 + 116*x^66 + 81*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 9*x^27 + 116*x^26 + 127*x^25 + 62*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 122*x^20 + 77*x^19 + 44*x^18 + 75*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 55*x^11 + 124*x^10 + 97*x^9 + 18*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 70*x^4 + 75*x^3 + 36*x^2 + 125*x + 114, x^95 + 15*x^93 + 22*x^92 + 53*x^91 + 92*x^90 + 83*x^89 + 2*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 22*x^84 + 9*x^83 + 68*x^82 + 15*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 115*x^75 + 84*x^74 + 101*x^73 + 126*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 26*x^68 + 119*x^67 + 76*x^66 + 17*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 105*x^27 + 12*x^26 + 63*x^25 + 10*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 46*x^20 + 109*x^19 + 20*x^18 + 11*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 87*x^11 + 4*x^10 + 33*x^9 + 38*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 82*x^4 + 43*x^3 + 28*x^2 + 61*x + 102, x^95 + 15*x^93 + 118*x^92 + 117*x^91 + 60*x^90 + 83*x^89 + 66*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 54*x^84 + 73*x^83 + 100*x^82 + 15*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 51*x^75 + 116*x^74 + 101*x^73 + 62*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 122*x^68 + 55*x^67 + 44*x^66 + 17*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 41*x^27 + 108*x^26 + 63*x^25 + 74*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 78*x^20 + 45*x^19 + 52*x^18 + 11*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 23*x^11 + 36*x^10 + 33*x^9 + 102*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 50*x^4 + 107*x^3 + 124*x^2 + 61*x + 102, x^95 + 15*x^93 + 82*x^92 + 85*x^91 + 4*x^90 + 19*x^89 + 70*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 50*x^84 + 105*x^83 + 28*x^82 + 79*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 83*x^75 + 76*x^74 + 37*x^73 + 122*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 30*x^68 + 23*x^67 + 84*x^66 + 81*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 9*x^27 + 84*x^26 + 127*x^25 + 94*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 58*x^20 + 77*x^19 + 76*x^18 + 75*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 55*x^11 + 28*x^10 + 97*x^9 + 114*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 6*x^4 + 75*x^3 + 4*x^2 + 125*x + 18, x^95 + 15*x^93 + 58*x^92 + 85*x^91 + 4*x^90 + 115*x^89 + 110*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 58*x^84 + 105*x^83 + 92*x^82 + 111*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 83*x^75 + 76*x^74 + 69*x^73 + 18*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 22*x^68 + 23*x^67 + 20*x^66 + 49*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 9*x^27 + 84*x^26 + 95*x^25 + 38*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 98*x^20 + 77*x^19 + 12*x^18 + 107*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 55*x^11 + 28*x^10 + x^9 + 42*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 30*x^4 + 75*x^3 + 68*x^2 + 93*x + 106, x^95 + 15*x^93 + 18*x^92 + 69*x^91 + 84*x^90 + 99*x^89 + 54*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 18*x^84 + 57*x^83 + 12*x^82 + 63*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 35*x^75 + 60*x^74 + 21*x^73 + 74*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 126*x^68 + 7*x^67 + 36*x^66 + 33*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 57*x^27 + 100*x^26 + 15*x^25 + 14*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 26*x^20 + 93*x^19 + 124*x^18 + 123*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 71*x^11 + 76*x^10 + 17*x^9 + 2*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 102*x^4 + 123*x^3 + 20*x^2 + 13*x + 66, x^95 + 15*x^93 + 66*x^92 + 5*x^91 + 20*x^90 + 99*x^89 + 38*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 2*x^84 + 121*x^83 + 76*x^82 + 63*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 99*x^75 + 124*x^74 + 21*x^73 + 90*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 14*x^68 + 71*x^67 + 100*x^66 + 33*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 121*x^27 + 36*x^26 + 15*x^25 + 62*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 74*x^20 + 29*x^19 + 60*x^18 + 123*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 7*x^11 + 12*x^10 + 17*x^9 + 82*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 54*x^4 + 59*x^3 + 84*x^2 + 13*x + 82, x^95 + 15*x^93 + 78*x^92 + 37*x^91 + 108*x^90 + 67*x^89 + 42*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 78*x^84 + 89*x^83 + 52*x^82 + 95*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 67*x^75 + 4*x^74 + 53*x^73 + 86*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 34*x^68 + 103*x^67 + 28*x^66 + x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 25*x^27 + 92*x^26 + 111*x^25 + 82*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 70*x^20 + 125*x^19 + 68*x^18 + 27*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 103*x^11 + 116*x^10 + 49*x^9 + 30*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 58*x^4 + 91*x^3 + 44*x^2 + 109*x + 94, x^95 + 15*x^93 + 58*x^92 + 69*x^91 + 84*x^90 + 3*x^89 + 94*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 90*x^84 + 57*x^83 + 76*x^82 + 31*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 35*x^75 + 60*x^74 + 117*x^73 + 98*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 54*x^68 + 7*x^67 + 100*x^66 + 65*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 57*x^27 + 100*x^26 + 47*x^25 + 86*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 2*x^20 + 93*x^19 + 60*x^18 + 91*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 71*x^11 + 76*x^10 + 113*x^9 + 58*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 62*x^4 + 123*x^3 + 84*x^2 + 45*x + 26, x^95 + 15*x^93 + 42*x^92 + 37*x^91 + 20*x^90 + 35*x^89 + 78*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 10*x^84 + 89*x^83 + 12*x^82 + 127*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 67*x^75 + 124*x^74 + 85*x^73 + 114*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 6*x^68 + 103*x^67 + 36*x^66 + 97*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 25*x^27 + 36*x^26 + 79*x^25 + 6*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 114*x^20 + 125*x^19 + 124*x^18 + 59*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 103*x^11 + 12*x^10 + 81*x^9 + 10*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 78*x^4 + 91*x^3 + 20*x^2 + 77*x + 42, x^95 + 15*x^93 + 74*x^92 + 37*x^91 + 84*x^90 + 99*x^89 + 110*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 42*x^84 + 89*x^83 + 76*x^82 + 63*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 67*x^75 + 60*x^74 + 21*x^73 + 82*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 102*x^68 + 103*x^67 + 100*x^66 + 33*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 25*x^27 + 100*x^26 + 15*x^25 + 38*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 18*x^20 + 125*x^19 + 60*x^18 + 123*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 103*x^11 + 76*x^10 + 17*x^9 + 106*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 46*x^4 + 91*x^3 + 84*x^2 + 13*x + 10, x^95 + 15*x^93 + 126*x^92 + 21*x^91 + 92*x^90 + 19*x^89 + 42*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 30*x^84 + 41*x^83 + 4*x^82 + 79*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 19*x^75 + 84*x^74 + 37*x^73 + 22*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 18*x^68 + 87*x^67 + 12*x^66 + 81*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 73*x^27 + 12*x^26 + 127*x^25 + 82*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 86*x^20 + 13*x^19 + 84*x^18 + 75*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 119*x^11 + 4*x^10 + 97*x^9 + 94*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 106*x^4 + 11*x^3 + 92*x^2 + 125*x + 62, x^95 + 15*x^93 + 122*x^92 + 117*x^91 + 100*x^90 + 19*x^89 + 14*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 58*x^84 + 73*x^83 + 124*x^82 + 79*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 51*x^75 + 108*x^74 + 37*x^73 + 114*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 22*x^68 + 55*x^67 + 116*x^66 + 81*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 41*x^27 + 52*x^26 + 127*x^25 + 70*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 98*x^20 + 45*x^19 + 44*x^18 + 75*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 23*x^11 + 60*x^10 + 97*x^9 + 10*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 30*x^4 + 107*x^3 + 36*x^2 + 125*x + 10, x^95 + 15*x^93 + 70*x^92 + 101*x^91 + 108*x^90 + 99*x^89 + 98*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 38*x^84 + 25*x^83 + 116*x^82 + 63*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 3*x^75 + 4*x^74 + 21*x^73 + 94*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 74*x^68 + 39*x^67 + 92*x^66 + 33*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 89*x^27 + 92*x^26 + 15*x^25 + 106*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 126*x^20 + 61*x^19 + 4*x^18 + 123*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 39*x^11 + 116*x^10 + 17*x^9 + 6*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 66*x^4 + 27*x^3 + 108*x^2 + 13*x + 38, x^95 + 15*x^93 + 74*x^92 + 101*x^91 + 52*x^90 + 99*x^89 + 78*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 106*x^84 + 25*x^83 + 108*x^82 + 63*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 3*x^75 + 92*x^74 + 21*x^73 + 114*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 38*x^68 + 39*x^67 + 68*x^66 + 33*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 89*x^27 + 68*x^26 + 15*x^25 + 6*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 82*x^20 + 61*x^19 + 92*x^18 + 123*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 39*x^11 + 108*x^10 + 17*x^9 + 10*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 110*x^4 + 27*x^3 + 52*x^2 + 13*x + 106, x^95 + 15*x^93 + 2*x^92 + 85*x^91 + 100*x^90 + 19*x^89 + 86*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 98*x^84 + 105*x^83 + 60*x^82 + 79*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 83*x^75 + 108*x^74 + 37*x^73 + 106*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 110*x^68 + 23*x^67 + 52*x^66 + 81*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 9*x^27 + 52*x^26 + 127*x^25 + 46*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 42*x^20 + 77*x^19 + 108*x^18 + 75*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 55*x^11 + 60*x^10 + 97*x^9 + 34*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 22*x^4 + 75*x^3 + 100*x^2 + 125*x + 66, x^95 + 15*x^93 + 2*x^92 + 5*x^91 + 52*x^90 + 99*x^89 + 70*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 2*x^84 + 121*x^83 + 44*x^82 + 63*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 99*x^75 + 92*x^74 + 21*x^73 + 58*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 14*x^68 + 71*x^67 + 4*x^66 + 33*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 121*x^27 + 68*x^26 + 15*x^25 + 94*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 74*x^20 + 29*x^19 + 28*x^18 + 123*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 7*x^11 + 108*x^10 + 17*x^9 + 50*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 54*x^4 + 59*x^3 + 116*x^2 + 13*x + 114, x^95 + 15*x^93 + 86*x^92 + 117*x^91 + 28*x^90 + 83*x^89 + 66*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 86*x^84 + 73*x^83 + 4*x^82 + 15*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 51*x^75 + 20*x^74 + 101*x^73 + 62*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 90*x^68 + 55*x^67 + 12*x^66 + 17*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 41*x^27 + 76*x^26 + 63*x^25 + 74*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 110*x^20 + 45*x^19 + 84*x^18 + 11*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 23*x^11 + 68*x^10 + 33*x^9 + 102*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 18*x^4 + 107*x^3 + 92*x^2 + 61*x + 38, x^95 + 15*x^93 + 30*x^92 + 101*x^91 + 76*x^90 + 3*x^89 + 90*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 30*x^84 + 25*x^83 + 84*x^82 + 31*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 3*x^75 + 36*x^74 + 117*x^73 + 38*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 82*x^68 + 39*x^67 + 124*x^66 + 65*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 89*x^27 + 60*x^26 + 47*x^25 + 66*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 86*x^20 + 61*x^19 + 100*x^18 + 91*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 39*x^11 + 20*x^10 + 113*x^9 + 46*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 42*x^4 + 27*x^3 + 12*x^2 + 45*x + 110, x^95 + 15*x^93 + 98*x^92 + 117*x^91 + 100*x^90 + 51*x^89 + 118*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 66*x^84 + 73*x^83 + 60*x^82 + 47*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 51*x^75 + 108*x^74 + 5*x^73 + 74*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 14*x^68 + 55*x^67 + 52*x^66 + 113*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 41*x^27 + 52*x^26 + 31*x^25 + 78*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 10*x^20 + 45*x^19 + 108*x^18 + 43*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 23*x^11 + 60*x^10 + 65*x^9 + 2*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 54*x^4 + 107*x^3 + 100*x^2 + 29*x + 34, x^95 + 15*x^93 + 10*x^92 + 101*x^91 + 84*x^90 + 99*x^89 + 110*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 106*x^84 + 25*x^83 + 76*x^82 + 63*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 3*x^75 + 60*x^74 + 21*x^73 + 82*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 38*x^68 + 39*x^67 + 100*x^66 + 33*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 89*x^27 + 100*x^26 + 15*x^25 + 38*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 82*x^20 + 61*x^19 + 60*x^18 + 123*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 39*x^11 + 76*x^10 + 17*x^9 + 106*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 110*x^4 + 27*x^3 + 84*x^2 + 13*x + 10, x^95 + 15*x^93 + 114*x^92 + 53*x^91 + 4*x^90 + 115*x^89 + 38*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 82*x^84 + 9*x^83 + 28*x^82 + 111*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 115*x^75 + 76*x^74 + 69*x^73 + 26*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 126*x^68 + 119*x^67 + 84*x^66 + 49*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 105*x^27 + 84*x^26 + 95*x^25 + 62*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 90*x^20 + 109*x^19 + 76*x^18 + 107*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 87*x^11 + 28*x^10 + x^9 + 18*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 102*x^4 + 43*x^3 + 4*x^2 + 93*x + 50, x^95 + 15*x^93 + 66*x^92 + 101*x^91 + 116*x^90 + 3*x^89 + 70*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 66*x^84 + 25*x^83 + 108*x^82 + 31*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 3*x^75 + 28*x^74 + 117*x^73 + 58*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 78*x^68 + 39*x^67 + 68*x^66 + 65*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 89*x^27 + 4*x^26 + 47*x^25 + 94*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 10*x^20 + 61*x^19 + 92*x^18 + 91*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 39*x^11 + 44*x^10 + 113*x^9 + 50*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 118*x^4 + 27*x^3 + 52*x^2 + 45*x + 114, x^95 + 15*x^93 + 126*x^92 + 37*x^91 + 12*x^90 + 67*x^89 + 122*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 126*x^84 + 89*x^83 + 20*x^82 + 95*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 67*x^75 + 100*x^74 + 53*x^73 + 6*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 114*x^68 + 103*x^67 + 60*x^66 + x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 25*x^27 + 124*x^26 + 111*x^25 + 98*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 54*x^20 + 125*x^19 + 36*x^18 + 27*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 103*x^11 + 84*x^10 + 49*x^9 + 14*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 74*x^4 + 91*x^3 + 76*x^2 + 109*x + 78, x^95 + 15*x^93 + 118*x^92 + 21*x^91 + 60*x^90 + 115*x^89 + 2*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 54*x^84 + 41*x^83 + 100*x^82 + 111*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 19*x^75 + 116*x^74 + 69*x^73 + 126*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 122*x^68 + 87*x^67 + 44*x^66 + 49*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 73*x^27 + 108*x^26 + 95*x^25 + 10*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 78*x^20 + 13*x^19 + 52*x^18 + 107*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 119*x^11 + 36*x^10 + x^9 + 38*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 50*x^4 + 11*x^3 + 124*x^2 + 93*x + 38, x^95 + 15*x^93 + 70*x^92 + 117*x^91 + 92*x^90 + 19*x^89 + 114*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 6*x^84 + 73*x^83 + 68*x^82 + 79*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 51*x^75 + 84*x^74 + 37*x^73 + 14*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 42*x^68 + 55*x^67 + 76*x^66 + 81*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 41*x^27 + 12*x^26 + 127*x^25 + 58*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 94*x^20 + 45*x^19 + 20*x^18 + 75*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 23*x^11 + 4*x^10 + 97*x^9 + 118*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 34*x^4 + 107*x^3 + 28*x^2 + 125*x + 118, x^95 + 15*x^93 + 58*x^92 + 69*x^91 + 52*x^90 + 3*x^89 + 126*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 26*x^84 + 57*x^83 + 108*x^82 + 31*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 35*x^75 + 92*x^74 + 117*x^73 + 66*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 118*x^68 + 7*x^67 + 68*x^66 + 65*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 57*x^27 + 68*x^26 + 47*x^25 + 118*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 66*x^20 + 93*x^19 + 92*x^18 + 91*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 71*x^11 + 108*x^10 + 113*x^9 + 26*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 126*x^4 + 123*x^3 + 52*x^2 + 45*x + 58, x^95 + 15*x^93 + 102*x^92 + 21*x^91 + 28*x^90 + 51*x^89 + 18*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 38*x^84 + 41*x^83 + 4*x^82 + 47*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 19*x^75 + 20*x^74 + 5*x^73 + 110*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 10*x^68 + 87*x^67 + 12*x^66 + 113*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 73*x^27 + 76*x^26 + 31*x^25 + 90*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 126*x^20 + 13*x^19 + 84*x^18 + 43*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 119*x^11 + 68*x^10 + 65*x^9 + 86*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 2*x^4 + 11*x^3 + 92*x^2 + 29*x + 86, x^95 + 15*x^93 + 90*x^92 + 69*x^91 + 52*x^90 + 3*x^89 + 30*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 58*x^84 + 57*x^83 + 108*x^82 + 31*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 35*x^75 + 92*x^74 + 117*x^73 + 34*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 86*x^68 + 7*x^67 + 68*x^66 + 65*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 57*x^27 + 68*x^26 + 47*x^25 + 22*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 98*x^20 + 93*x^19 + 92*x^18 + 91*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 71*x^11 + 108*x^10 + 113*x^9 + 122*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 94*x^4 + 123*x^3 + 52*x^2 + 45*x + 26, x^95 + 15*x^93 + 18*x^92 + 85*x^91 + 68*x^90 + 83*x^89 + 6*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 114*x^84 + 105*x^83 + 92*x^82 + 15*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 83*x^75 + 12*x^74 + 101*x^73 + 58*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 94*x^68 + 23*x^67 + 20*x^66 + 17*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 9*x^27 + 20*x^26 + 63*x^25 + 30*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 122*x^20 + 77*x^19 + 12*x^18 + 11*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 55*x^11 + 92*x^10 + 33*x^9 + 50*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 70*x^4 + 75*x^3 + 68*x^2 + 61*x + 82, x^95 + 15*x^93 + 22*x^92 + 53*x^91 + 28*x^90 + 19*x^89 + 2*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 22*x^84 + 9*x^83 + 4*x^82 + 79*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 115*x^75 + 20*x^74 + 37*x^73 + 126*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 26*x^68 + 119*x^67 + 12*x^66 + 81*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 105*x^27 + 76*x^26 + 127*x^25 + 10*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 46*x^20 + 109*x^19 + 84*x^18 + 75*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 87*x^11 + 68*x^10 + 97*x^9 + 38*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 82*x^4 + 43*x^3 + 92*x^2 + 125*x + 102, x^95 + 15*x^93 + 98*x^92 + 53*x^91 + 100*x^90 + 51*x^89 + 54*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 66*x^84 + 9*x^83 + 60*x^82 + 47*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 115*x^75 + 108*x^74 + 5*x^73 + 10*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 14*x^68 + 119*x^67 + 52*x^66 + 113*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 105*x^27 + 52*x^26 + 31*x^25 + 14*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 10*x^20 + 109*x^19 + 108*x^18 + 43*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 87*x^11 + 60*x^10 + 65*x^9 + 66*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 54*x^4 + 43*x^3 + 100*x^2 + 29*x + 98, x^95 + 15*x^93 + 86*x^92 + 85*x^91 + 60*x^90 + 115*x^89 + 34*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 22*x^84 + 105*x^83 + 100*x^82 + 111*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 83*x^75 + 116*x^74 + 69*x^73 + 94*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 26*x^68 + 23*x^67 + 44*x^66 + 49*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 9*x^27 + 108*x^26 + 95*x^25 + 42*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 46*x^20 + 77*x^19 + 52*x^18 + 107*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 55*x^11 + 36*x^10 + x^9 + 6*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 82*x^4 + 75*x^3 + 124*x^2 + 93*x + 6, x^95 + 15*x^93 + 82*x^92 + 101*x^91 + 20*x^90 + 67*x^89 + 54*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 82*x^84 + 25*x^83 + 76*x^82 + 95*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 3*x^75 + 124*x^74 + 53*x^73 + 74*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 62*x^68 + 39*x^67 + 100*x^66 + x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 89*x^27 + 36*x^26 + 111*x^25 + 14*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 90*x^20 + 61*x^19 + 60*x^18 + 27*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 39*x^11 + 12*x^10 + 49*x^9 + 2*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 38*x^4 + 27*x^3 + 84*x^2 + 109*x + 66, x^95 + 15*x^93 + 38*x^92 + 21*x^91 + 60*x^90 + 51*x^89 + 50*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 38*x^84 + 41*x^83 + 100*x^82 + 47*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 19*x^75 + 116*x^74 + 5*x^73 + 78*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 10*x^68 + 87*x^67 + 44*x^66 + 113*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 73*x^27 + 108*x^26 + 31*x^25 + 122*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 126*x^20 + 13*x^19 + 52*x^18 + 43*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 119*x^11 + 36*x^10 + 65*x^9 + 54*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 2*x^4 + 11*x^3 + 124*x^2 + 29*x + 118, x^95 + 15*x^93 + 10*x^92 + 37*x^91 + 84*x^90 + 99*x^89 + 46*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 106*x^84 + 89*x^83 + 76*x^82 + 63*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 67*x^75 + 60*x^74 + 21*x^73 + 18*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 38*x^68 + 103*x^67 + 100*x^66 + 33*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 25*x^27 + 100*x^26 + 15*x^25 + 102*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 82*x^20 + 125*x^19 + 60*x^18 + 123*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 103*x^11 + 76*x^10 + 17*x^9 + 42*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 110*x^4 + 91*x^3 + 84*x^2 + 13*x + 74, x^95 + 15*x^93 + 54*x^92 + 85*x^91 + 92*x^90 + 115*x^89 + 98*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 54*x^84 + 105*x^83 + 68*x^82 + 111*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 83*x^75 + 84*x^74 + 69*x^73 + 30*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 122*x^68 + 23*x^67 + 76*x^66 + 49*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 9*x^27 + 12*x^26 + 95*x^25 + 106*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 78*x^20 + 77*x^19 + 20*x^18 + 107*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 55*x^11 + 4*x^10 + x^9 + 70*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 50*x^4 + 75*x^3 + 28*x^2 + 93*x + 6, x^95 + 15*x^93 + 6*x^92 + 69*x^91 + 76*x^90 + 3*x^89 + 66*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 38*x^84 + 57*x^83 + 20*x^82 + 31*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 35*x^75 + 36*x^74 + 117*x^73 + 126*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 74*x^68 + 7*x^67 + 60*x^66 + 65*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 57*x^27 + 60*x^26 + 47*x^25 + 74*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 126*x^20 + 93*x^19 + 36*x^18 + 91*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 71*x^11 + 20*x^10 + 113*x^9 + 38*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 66*x^4 + 123*x^3 + 76*x^2 + 45*x + 6, x^95 + 15*x^93 + 22*x^92 + 37*x^91 + 44*x^90 + 35*x^89 + 50*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 54*x^84 + 89*x^83 + 52*x^82 + 127*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 67*x^75 + 68*x^74 + 85*x^73 + 14*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 58*x^68 + 103*x^67 + 28*x^66 + 97*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 25*x^27 + 28*x^26 + 79*x^25 + 122*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 78*x^20 + 125*x^19 + 68*x^18 + 59*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 103*x^11 + 52*x^10 + 81*x^9 + 118*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 114*x^4 + 91*x^3 + 44*x^2 + 77*x + 86, x^95 + 15*x^93 + 58*x^92 + 5*x^91 + 116*x^90 + 67*x^89 + 62*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 26*x^84 + 121*x^83 + 44*x^82 + 95*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 99*x^75 + 28*x^74 + 53*x^73 + 2*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 118*x^68 + 71*x^67 + 4*x^66 + x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 121*x^27 + 4*x^26 + 111*x^25 + 54*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 66*x^20 + 29*x^19 + 28*x^18 + 27*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 7*x^11 + 44*x^10 + 49*x^9 + 90*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 126*x^4 + 59*x^3 + 116*x^2 + 109*x + 122, x^95 + 15*x^93 + 58*x^92 + 85*x^91 + 100*x^90 + 115*x^89 + 14*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 122*x^84 + 105*x^83 + 124*x^82 + 111*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 83*x^75 + 108*x^74 + 69*x^73 + 114*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 86*x^68 + 23*x^67 + 116*x^66 + 49*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 9*x^27 + 52*x^26 + 95*x^25 + 70*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 34*x^20 + 77*x^19 + 44*x^18 + 107*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 55*x^11 + 60*x^10 + x^9 + 10*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 94*x^4 + 75*x^3 + 36*x^2 + 93*x + 10, x^95 + 15*x^93 + 26*x^92 + 117*x^91 + 36*x^90 + 83*x^89 + 46*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 90*x^84 + 73*x^83 + 60*x^82 + 15*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 51*x^75 + 44*x^74 + 101*x^73 + 82*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 118*x^68 + 55*x^67 + 52*x^66 + 17*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 41*x^27 + 116*x^26 + 63*x^25 + 102*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 2*x^20 + 45*x^19 + 108*x^18 + 11*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 23*x^11 + 124*x^10 + 33*x^9 + 106*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 126*x^4 + 107*x^3 + 100*x^2 + 61*x + 106, x^95 + 15*x^93 + 62*x^92 + 21*x^91 + 92*x^90 + 19*x^89 + 106*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 94*x^84 + 41*x^83 + 4*x^82 + 79*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 19*x^75 + 84*x^74 + 37*x^73 + 86*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 82*x^68 + 87*x^67 + 12*x^66 + 81*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 73*x^27 + 12*x^26 + 127*x^25 + 18*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 22*x^20 + 13*x^19 + 84*x^18 + 75*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 119*x^11 + 4*x^10 + 97*x^9 + 30*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 42*x^4 + 11*x^3 + 92*x^2 + 125*x + 126, x^95 + 15*x^93 + 78*x^92 + 117*x^91 + 28*x^90 + 51*x^89 + 122*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 46*x^84 + 73*x^83 + 68*x^82 + 47*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 51*x^75 + 20*x^74 + 5*x^73 + 70*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 2*x^68 + 55*x^67 + 76*x^66 + 113*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 41*x^27 + 76*x^26 + 31*x^25 + 98*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 38*x^20 + 45*x^19 + 20*x^18 + 43*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 23*x^11 + 68*x^10 + 65*x^9 + 78*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 26*x^4 + 107*x^3 + 28*x^2 + 29*x + 110, x^95 + 15*x^93 + 74*x^92 + 5*x^91 + 84*x^90 + 3*x^89 + 110*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 42*x^84 + 121*x^83 + 76*x^82 + 31*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 99*x^75 + 60*x^74 + 117*x^73 + 82*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 102*x^68 + 71*x^67 + 100*x^66 + 65*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 121*x^27 + 100*x^26 + 47*x^25 + 38*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 18*x^20 + 29*x^19 + 60*x^18 + 91*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 7*x^11 + 76*x^10 + 113*x^9 + 106*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 46*x^4 + 59*x^3 + 84*x^2 + 45*x + 10, x^95 + 15*x^93 + 62*x^92 + 101*x^91 + 108*x^90 + 3*x^89 + 90*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 126*x^84 + 25*x^83 + 52*x^82 + 31*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 3*x^75 + 4*x^74 + 117*x^73 + 38*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 114*x^68 + 39*x^67 + 28*x^66 + 65*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 89*x^27 + 92*x^26 + 47*x^25 + 66*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 54*x^20 + 61*x^19 + 68*x^18 + 91*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 39*x^11 + 116*x^10 + 113*x^9 + 46*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 74*x^4 + 27*x^3 + 44*x^2 + 45*x + 46, x^95 + 15*x^93 + 114*x^92 + 69*x^91 + 116*x^90 + 35*x^89 + 54*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 50*x^84 + 57*x^83 + 108*x^82 + 127*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 35*x^75 + 28*x^74 + 85*x^73 + 74*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 94*x^68 + 7*x^67 + 68*x^66 + 97*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 57*x^27 + 4*x^26 + 79*x^25 + 14*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 58*x^20 + 93*x^19 + 92*x^18 + 59*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 71*x^11 + 44*x^10 + 81*x^9 + 2*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 70*x^4 + 123*x^3 + 52*x^2 + 77*x + 2, x^95 + 15*x^93 + 18*x^92 + 5*x^91 + 116*x^90 + 99*x^89 + 86*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 82*x^84 + 121*x^83 + 108*x^82 + 63*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 99*x^75 + 28*x^74 + 21*x^73 + 42*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 62*x^68 + 71*x^67 + 68*x^66 + 33*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 121*x^27 + 4*x^26 + 15*x^25 + 46*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 90*x^20 + 29*x^19 + 92*x^18 + 123*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 7*x^11 + 44*x^10 + 17*x^9 + 98*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 38*x^4 + 59*x^3 + 52*x^2 + 13*x + 98, x^95 + 15*x^93 + 34*x^92 + 5*x^91 + 116*x^90 + 99*x^89 + 38*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 34*x^84 + 121*x^83 + 108*x^82 + 63*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 99*x^75 + 28*x^74 + 21*x^73 + 90*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 110*x^68 + 71*x^67 + 68*x^66 + 33*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 121*x^27 + 4*x^26 + 15*x^25 + 62*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 106*x^20 + 29*x^19 + 92*x^18 + 123*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 7*x^11 + 44*x^10 + 17*x^9 + 82*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 22*x^4 + 59*x^3 + 52*x^2 + 13*x + 18, x^95 + 15*x^93 + 34*x^92 + 37*x^91 + 84*x^90 + 67*x^89 + 70*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 98*x^84 + 89*x^83 + 12*x^82 + 95*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 67*x^75 + 60*x^74 + 53*x^73 + 58*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 46*x^68 + 103*x^67 + 36*x^66 + x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 25*x^27 + 100*x^26 + 111*x^25 + 94*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 42*x^20 + 125*x^19 + 124*x^18 + 27*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 103*x^11 + 76*x^10 + 49*x^9 + 50*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 86*x^4 + 91*x^3 + 20*x^2 + 109*x + 50, x^95 + 15*x^93 + 30*x^92 + 101*x^91 + 12*x^90 + 3*x^89 + 26*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 30*x^84 + 25*x^83 + 20*x^82 + 31*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 3*x^75 + 100*x^74 + 117*x^73 + 102*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 82*x^68 + 39*x^67 + 60*x^66 + 65*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 89*x^27 + 124*x^26 + 47*x^25 + 2*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 86*x^20 + 61*x^19 + 36*x^18 + 91*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 39*x^11 + 84*x^10 + 113*x^9 + 110*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 42*x^4 + 27*x^3 + 76*x^2 + 45*x + 46, x^95 + 15*x^93 + 94*x^92 + 37*x^91 + 12*x^90 + 67*x^89 + 90*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 94*x^84 + 89*x^83 + 20*x^82 + 95*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 67*x^75 + 100*x^74 + 53*x^73 + 38*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 18*x^68 + 103*x^67 + 60*x^66 + x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 25*x^27 + 124*x^26 + 111*x^25 + 66*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 22*x^20 + 125*x^19 + 36*x^18 + 27*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 103*x^11 + 84*x^10 + 49*x^9 + 46*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 106*x^4 + 91*x^3 + 76*x^2 + 109*x + 110, x^95 + 15*x^93 + 10*x^92 + 85*x^91 + 68*x^90 + 51*x^89 + 126*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 74*x^84 + 105*x^83 + 28*x^82 + 47*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 83*x^75 + 12*x^74 + 5*x^73 + 2*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 6*x^68 + 23*x^67 + 84*x^66 + 113*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 9*x^27 + 20*x^26 + 31*x^25 + 118*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 50*x^20 + 77*x^19 + 76*x^18 + 43*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 55*x^11 + 92*x^10 + 65*x^9 + 90*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 78*x^4 + 75*x^3 + 4*x^2 + 29*x + 90, x^95 + 15*x^93 + 110*x^92 + 5*x^91 + 76*x^90 + 35*x^89 + 42*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 46*x^84 + 121*x^83 + 84*x^82 + 127*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 99*x^75 + 36*x^74 + 85*x^73 + 86*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 66*x^68 + 71*x^67 + 124*x^66 + 97*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 121*x^27 + 60*x^26 + 79*x^25 + 82*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 38*x^20 + 29*x^19 + 100*x^18 + 59*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 7*x^11 + 20*x^10 + 81*x^9 + 30*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 90*x^4 + 59*x^3 + 12*x^2 + 77*x + 30, x^95 + 15*x^93 + 102*x^92 + 117*x^91 + 28*x^90 + 19*x^89 + 82*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 38*x^84 + 73*x^83 + 4*x^82 + 79*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 51*x^75 + 20*x^74 + 37*x^73 + 46*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 10*x^68 + 55*x^67 + 12*x^66 + 81*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 41*x^27 + 76*x^26 + 127*x^25 + 26*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 126*x^20 + 45*x^19 + 84*x^18 + 75*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 23*x^11 + 68*x^10 + 97*x^9 + 22*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 2*x^4 + 107*x^3 + 92*x^2 + 125*x + 22, x^95 + 15*x^93 + 70*x^92 + 21*x^91 + 60*x^90 + 51*x^89 + 82*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 70*x^84 + 41*x^83 + 100*x^82 + 47*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 19*x^75 + 116*x^74 + 5*x^73 + 46*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 106*x^68 + 87*x^67 + 44*x^66 + 113*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 73*x^27 + 108*x^26 + 31*x^25 + 26*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 30*x^20 + 13*x^19 + 52*x^18 + 43*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 119*x^11 + 36*x^10 + 65*x^9 + 22*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 98*x^4 + 11*x^3 + 124*x^2 + 29*x + 86, x^95 + 15*x^93 + 22*x^92 + 117*x^91 + 92*x^90 + 83*x^89 + 66*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 22*x^84 + 73*x^83 + 68*x^82 + 15*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 51*x^75 + 84*x^74 + 101*x^73 + 62*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 26*x^68 + 55*x^67 + 76*x^66 + 17*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 41*x^27 + 12*x^26 + 63*x^25 + 74*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 46*x^20 + 45*x^19 + 20*x^18 + 11*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 23*x^11 + 4*x^10 + 33*x^9 + 102*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 82*x^4 + 107*x^3 + 28*x^2 + 61*x + 38, x^95 + 15*x^93 + 26*x^92 + 101*x^91 + 84*x^90 + 35*x^89 + 126*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 58*x^84 + 25*x^83 + 76*x^82 + 127*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 3*x^75 + 60*x^74 + 85*x^73 + 66*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 86*x^68 + 39*x^67 + 100*x^66 + 97*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 89*x^27 + 100*x^26 + 79*x^25 + 118*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 98*x^20 + 61*x^19 + 60*x^18 + 59*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 39*x^11 + 76*x^10 + 81*x^9 + 26*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 94*x^4 + 27*x^3 + 84*x^2 + 77*x + 122, x^95 + 15*x^93 + 46*x^92 + 101*x^91 + 44*x^90 + 67*x^89 + 10*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 46*x^84 + 25*x^83 + 116*x^82 + 95*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 3*x^75 + 68*x^74 + 53*x^73 + 118*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 66*x^68 + 39*x^67 + 92*x^66 + x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 89*x^27 + 28*x^26 + 111*x^25 + 50*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 38*x^20 + 61*x^19 + 4*x^18 + 27*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 39*x^11 + 52*x^10 + 49*x^9 + 62*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 90*x^4 + 27*x^3 + 108*x^2 + 109*x + 126, x^95 + 15*x^93 + 86*x^92 + 21*x^91 + 92*x^90 + 51*x^89 + 2*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 86*x^84 + 41*x^83 + 68*x^82 + 47*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 19*x^75 + 84*x^74 + 5*x^73 + 126*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 90*x^68 + 87*x^67 + 76*x^66 + 113*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 73*x^27 + 12*x^26 + 31*x^25 + 10*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 110*x^20 + 13*x^19 + 20*x^18 + 43*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 119*x^11 + 4*x^10 + 65*x^9 + 38*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 18*x^4 + 11*x^3 + 28*x^2 + 29*x + 102, x^95 + 15*x^93 + 122*x^92 + 117*x^91 + 100*x^90 + 83*x^89 + 78*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 58*x^84 + 73*x^83 + 124*x^82 + 15*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 51*x^75 + 108*x^74 + 101*x^73 + 50*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 22*x^68 + 55*x^67 + 116*x^66 + 17*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 41*x^27 + 52*x^26 + 63*x^25 + 6*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 98*x^20 + 45*x^19 + 44*x^18 + 11*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 23*x^11 + 60*x^10 + 33*x^9 + 74*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 30*x^4 + 107*x^3 + 36*x^2 + 61*x + 74, x^95 + 15*x^93 + 86*x^92 + 117*x^91 + 92*x^90 + 83*x^89 + 2*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 86*x^84 + 73*x^83 + 68*x^82 + 15*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 51*x^75 + 84*x^74 + 101*x^73 + 126*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 90*x^68 + 55*x^67 + 76*x^66 + 17*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 41*x^27 + 12*x^26 + 63*x^25 + 10*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 110*x^20 + 45*x^19 + 20*x^18 + 11*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 23*x^11 + 4*x^10 + 33*x^9 + 38*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 18*x^4 + 107*x^3 + 28*x^2 + 61*x + 102, x^95 + 15*x^93 + 18*x^92 + 37*x^91 + 20*x^90 + 3*x^89 + 118*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 18*x^84 + 89*x^83 + 76*x^82 + 31*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 67*x^75 + 124*x^74 + 117*x^73 + 10*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 126*x^68 + 103*x^67 + 100*x^66 + 65*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 25*x^27 + 36*x^26 + 47*x^25 + 78*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 26*x^20 + 125*x^19 + 60*x^18 + 91*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 103*x^11 + 12*x^10 + 113*x^9 + 66*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 102*x^4 + 91*x^3 + 84*x^2 + 45*x + 2, x^95 + 15*x^93 + 34*x^92 + 53*x^91 + 36*x^90 + 51*x^89 + 54*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 2*x^84 + 9*x^83 + 124*x^82 + 47*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 115*x^75 + 44*x^74 + 5*x^73 + 10*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 78*x^68 + 119*x^67 + 116*x^66 + 113*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 105*x^27 + 116*x^26 + 31*x^25 + 14*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 74*x^20 + 109*x^19 + 44*x^18 + 43*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 87*x^11 + 124*x^10 + 65*x^9 + 66*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 118*x^4 + 43*x^3 + 36*x^2 + 29*x + 98, x^95 + 15*x^93 + 50*x^92 + 5*x^91 + 116*x^90 + 35*x^89 + 54*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 114*x^84 + 121*x^83 + 108*x^82 + 127*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 99*x^75 + 28*x^74 + 85*x^73 + 74*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 30*x^68 + 71*x^67 + 68*x^66 + 97*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 121*x^27 + 4*x^26 + 79*x^25 + 14*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 122*x^20 + 29*x^19 + 92*x^18 + 59*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 7*x^11 + 44*x^10 + 81*x^9 + 2*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 6*x^4 + 59*x^3 + 52*x^2 + 77*x + 2, x^95 + 15*x^93 + 90*x^92 + 85*x^91 + 36*x^90 + 115*x^89 + 110*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 26*x^84 + 105*x^83 + 60*x^82 + 111*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 83*x^75 + 44*x^74 + 69*x^73 + 18*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 54*x^68 + 23*x^67 + 52*x^66 + 49*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 9*x^27 + 116*x^26 + 95*x^25 + 38*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 66*x^20 + 77*x^19 + 108*x^18 + 107*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 55*x^11 + 124*x^10 + x^9 + 42*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 62*x^4 + 75*x^3 + 100*x^2 + 93*x + 42, x^95 + 15*x^93 + 14*x^92 + 117*x^91 + 28*x^90 + 115*x^89 + 122*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 110*x^84 + 73*x^83 + 68*x^82 + 111*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 51*x^75 + 20*x^74 + 69*x^73 + 70*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 66*x^68 + 55*x^67 + 76*x^66 + 49*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 41*x^27 + 76*x^26 + 95*x^25 + 98*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 102*x^20 + 45*x^19 + 20*x^18 + 107*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 23*x^11 + 68*x^10 + x^9 + 78*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 90*x^4 + 107*x^3 + 28*x^2 + 93*x + 110, x^95 + 15*x^93 + 62*x^92 + 69*x^91 + 76*x^90 + 35*x^89 + 122*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 62*x^84 + 57*x^83 + 84*x^82 + 127*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 35*x^75 + 36*x^74 + 85*x^73 + 6*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 50*x^68 + 7*x^67 + 124*x^66 + 97*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 57*x^27 + 60*x^26 + 79*x^25 + 98*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 118*x^20 + 93*x^19 + 100*x^18 + 59*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 71*x^11 + 20*x^10 + 81*x^9 + 14*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 10*x^4 + 123*x^3 + 12*x^2 + 77*x + 78, x^95 + 15*x^93 + 2*x^92 + 5*x^91 + 84*x^90 + 99*x^89 + 38*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 66*x^84 + 121*x^83 + 12*x^82 + 63*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 99*x^75 + 60*x^74 + 21*x^73 + 90*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 78*x^68 + 71*x^67 + 36*x^66 + 33*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 121*x^27 + 100*x^26 + 15*x^25 + 62*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 10*x^20 + 29*x^19 + 124*x^18 + 123*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 7*x^11 + 76*x^10 + 17*x^9 + 82*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 118*x^4 + 59*x^3 + 20*x^2 + 13*x + 82, x^95 + 15*x^93 + 74*x^92 + 85*x^91 + 36*x^90 + 115*x^89 + 30*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 74*x^84 + 105*x^83 + 60*x^82 + 111*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 83*x^75 + 44*x^74 + 69*x^73 + 98*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 6*x^68 + 23*x^67 + 52*x^66 + 49*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 9*x^27 + 116*x^26 + 95*x^25 + 22*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 50*x^20 + 77*x^19 + 108*x^18 + 107*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 55*x^11 + 124*x^10 + x^9 + 58*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 78*x^4 + 75*x^3 + 100*x^2 + 93*x + 122, x^95 + 15*x^93 + 78*x^92 + 37*x^91 + 12*x^90 + 3*x^89 + 74*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 14*x^84 + 89*x^83 + 20*x^82 + 31*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 67*x^75 + 100*x^74 + 117*x^73 + 54*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 98*x^68 + 103*x^67 + 60*x^66 + 65*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 25*x^27 + 124*x^26 + 47*x^25 + 114*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 6*x^20 + 125*x^19 + 36*x^18 + 91*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 103*x^11 + 84*x^10 + 113*x^9 + 126*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 122*x^4 + 91*x^3 + 76*x^2 + 45*x + 126, x^95 + 15*x^93 + 66*x^92 + 21*x^91 + 68*x^90 + 19*x^89 + 118*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 98*x^84 + 41*x^83 + 92*x^82 + 79*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 19*x^75 + 12*x^74 + 37*x^73 + 74*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 110*x^68 + 87*x^67 + 20*x^66 + 81*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 73*x^27 + 20*x^26 + 127*x^25 + 78*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 42*x^20 + 13*x^19 + 12*x^18 + 75*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 119*x^11 + 92*x^10 + 97*x^9 + 2*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 22*x^4 + 11*x^3 + 68*x^2 + 125*x + 98, x^95 + 15*x^93 + 82*x^92 + 53*x^91 + 36*x^90 + 115*x^89 + 102*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 114*x^84 + 9*x^83 + 124*x^82 + 111*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 115*x^75 + 44*x^74 + 69*x^73 + 90*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 94*x^68 + 119*x^67 + 116*x^66 + 49*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 105*x^27 + 116*x^26 + 95*x^25 + 126*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 122*x^20 + 109*x^19 + 44*x^18 + 107*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 87*x^11 + 124*x^10 + x^9 + 82*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 70*x^4 + 43*x^3 + 36*x^2 + 93*x + 50, x^95 + 15*x^93 + 10*x^92 + 69*x^91 + 84*x^90 + 3*x^89 + 110*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 106*x^84 + 57*x^83 + 76*x^82 + 31*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 35*x^75 + 60*x^74 + 117*x^73 + 82*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 38*x^68 + 7*x^67 + 100*x^66 + 65*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 57*x^27 + 100*x^26 + 47*x^25 + 38*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 82*x^20 + 93*x^19 + 60*x^18 + 91*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 71*x^11 + 76*x^10 + 113*x^9 + 106*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 110*x^4 + 123*x^3 + 84*x^2 + 45*x + 10, x^95 + 15*x^93 + 30*x^92 + 53*x^91 + 60*x^90 + 51*x^89 + 42*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 126*x^84 + 9*x^83 + 36*x^82 + 47*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 115*x^75 + 116*x^74 + 5*x^73 + 22*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 50*x^68 + 119*x^67 + 108*x^66 + 113*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 105*x^27 + 108*x^26 + 31*x^25 + 82*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 54*x^20 + 109*x^19 + 116*x^18 + 43*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 87*x^11 + 36*x^10 + 65*x^9 + 94*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 10*x^4 + 43*x^3 + 60*x^2 + 29*x + 126, x^95 + 15*x^93 + 106*x^92 + 53*x^91 + 4*x^90 + 83*x^89 + 30*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 42*x^84 + 9*x^83 + 92*x^82 + 15*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 115*x^75 + 76*x^74 + 101*x^73 + 98*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 38*x^68 + 119*x^67 + 20*x^66 + 17*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 105*x^27 + 84*x^26 + 63*x^25 + 22*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 18*x^20 + 109*x^19 + 12*x^18 + 11*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 87*x^11 + 28*x^10 + 33*x^9 + 58*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 110*x^4 + 43*x^3 + 68*x^2 + 61*x + 58, x^95 + 15*x^93 + 18*x^92 + 69*x^91 + 20*x^90 + 99*x^89 + 118*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 18*x^84 + 57*x^83 + 76*x^82 + 63*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 35*x^75 + 124*x^74 + 21*x^73 + 10*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 126*x^68 + 7*x^67 + 100*x^66 + 33*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 57*x^27 + 36*x^26 + 15*x^25 + 78*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 26*x^20 + 93*x^19 + 60*x^18 + 123*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 71*x^11 + 12*x^10 + 17*x^9 + 66*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 102*x^4 + 123*x^3 + 84*x^2 + 13*x + 2, x^95 + 15*x^93 + 2*x^92 + 69*x^91 + 52*x^90 + 35*x^89 + 70*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 2*x^84 + 57*x^83 + 44*x^82 + 127*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 35*x^75 + 92*x^74 + 85*x^73 + 58*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 14*x^68 + 7*x^67 + 4*x^66 + 97*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 57*x^27 + 68*x^26 + 79*x^25 + 94*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 74*x^20 + 93*x^19 + 28*x^18 + 59*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 71*x^11 + 108*x^10 + 81*x^9 + 50*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 54*x^4 + 123*x^3 + 116*x^2 + 77*x + 114, x^95 + 15*x^93 + 54*x^92 + 117*x^91 + 60*x^90 + 83*x^89 + 2*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 118*x^84 + 73*x^83 + 100*x^82 + 15*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 51*x^75 + 116*x^74 + 101*x^73 + 126*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 58*x^68 + 55*x^67 + 44*x^66 + 17*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 41*x^27 + 108*x^26 + 63*x^25 + 10*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 14*x^20 + 45*x^19 + 52*x^18 + 11*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 23*x^11 + 36*x^10 + 33*x^9 + 38*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 114*x^4 + 107*x^3 + 124*x^2 + 61*x + 38, x^95 + 15*x^93 + 82*x^92 + 69*x^91 + 116*x^90 + 35*x^89 + 22*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 18*x^84 + 57*x^83 + 108*x^82 + 127*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 35*x^75 + 28*x^74 + 85*x^73 + 106*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 126*x^68 + 7*x^67 + 68*x^66 + 97*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 57*x^27 + 4*x^26 + 79*x^25 + 110*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 26*x^20 + 93*x^19 + 92*x^18 + 59*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 71*x^11 + 44*x^10 + 81*x^9 + 34*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 102*x^4 + 123*x^3 + 52*x^2 + 77*x + 34, x^95 + 15*x^93 + 54*x^92 + 53*x^91 + 92*x^90 + 19*x^89 + 98*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 54*x^84 + 9*x^83 + 68*x^82 + 79*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 115*x^75 + 84*x^74 + 37*x^73 + 30*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 122*x^68 + 119*x^67 + 76*x^66 + 81*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 105*x^27 + 12*x^26 + 127*x^25 + 106*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 78*x^20 + 109*x^19 + 20*x^18 + 75*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 87*x^11 + 4*x^10 + 97*x^9 + 70*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 50*x^4 + 43*x^3 + 28*x^2 + 125*x + 6, x^95 + 15*x^93 + 118*x^92 + 69*x^91 + 108*x^90 + 67*x^89 + 18*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 22*x^84 + 57*x^83 + 116*x^82 + 95*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 35*x^75 + 4*x^74 + 53*x^73 + 46*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 90*x^68 + 7*x^67 + 92*x^66 + x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 57*x^27 + 92*x^26 + 111*x^25 + 90*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 46*x^20 + 93*x^19 + 4*x^18 + 27*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 71*x^11 + 116*x^10 + 49*x^9 + 22*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 18*x^4 + 123*x^3 + 108*x^2 + 109*x + 118, x^95 + 15*x^93 + 74*x^92 + 85*x^91 + 100*x^90 + 51*x^89 + 30*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 74*x^84 + 105*x^83 + 124*x^82 + 47*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 83*x^75 + 108*x^74 + 5*x^73 + 98*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 6*x^68 + 23*x^67 + 116*x^66 + 113*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 9*x^27 + 52*x^26 + 31*x^25 + 22*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 50*x^20 + 77*x^19 + 44*x^18 + 43*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 55*x^11 + 60*x^10 + 65*x^9 + 58*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 78*x^4 + 75*x^3 + 36*x^2 + 29*x + 122, x^95 + 15*x^93 + 14*x^92 + 21*x^91 + 60*x^90 + 19*x^89 + 26*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 46*x^84 + 41*x^83 + 36*x^82 + 79*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 19*x^75 + 116*x^74 + 37*x^73 + 38*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 2*x^68 + 87*x^67 + 108*x^66 + 81*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 73*x^27 + 108*x^26 + 127*x^25 + 2*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 38*x^20 + 13*x^19 + 116*x^18 + 75*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 119*x^11 + 36*x^10 + 97*x^9 + 46*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 26*x^4 + 11*x^3 + 60*x^2 + 125*x + 14, x^95 + 15*x^93 + 18*x^92 + 21*x^91 + 68*x^90 + 83*x^89 + 70*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 114*x^84 + 41*x^83 + 92*x^82 + 15*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 19*x^75 + 12*x^74 + 101*x^73 + 122*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 94*x^68 + 87*x^67 + 20*x^66 + 17*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 73*x^27 + 20*x^26 + 63*x^25 + 94*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 122*x^20 + 13*x^19 + 12*x^18 + 11*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 119*x^11 + 92*x^10 + 33*x^9 + 114*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 70*x^4 + 11*x^3 + 68*x^2 + 61*x + 18, x^95 + 15*x^93 + 114*x^92 + 85*x^91 + 100*x^90 + 83*x^89 + 70*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 18*x^84 + 105*x^83 + 60*x^82 + 15*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 83*x^75 + 108*x^74 + 101*x^73 + 122*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 62*x^68 + 23*x^67 + 52*x^66 + 17*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 9*x^27 + 52*x^26 + 63*x^25 + 94*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 26*x^20 + 77*x^19 + 108*x^18 + 11*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 55*x^11 + 60*x^10 + 33*x^9 + 114*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 38*x^4 + 75*x^3 + 100*x^2 + 61*x + 82, x^95 + 15*x^93 + 14*x^92 + 85*x^91 + 28*x^90 + 83*x^89 + 58*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 110*x^84 + 105*x^83 + 68*x^82 + 15*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 83*x^75 + 20*x^74 + 101*x^73 + 6*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 66*x^68 + 23*x^67 + 76*x^66 + 17*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 9*x^27 + 76*x^26 + 63*x^25 + 34*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 102*x^20 + 77*x^19 + 20*x^18 + 11*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 55*x^11 + 68*x^10 + 33*x^9 + 14*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 90*x^4 + 75*x^3 + 28*x^2 + 61*x + 46, x^95 + 15*x^93 + 70*x^92 + 117*x^91 + 28*x^90 + 19*x^89 + 50*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 6*x^84 + 73*x^83 + 4*x^82 + 79*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 51*x^75 + 20*x^74 + 37*x^73 + 78*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 42*x^68 + 55*x^67 + 12*x^66 + 81*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 41*x^27 + 76*x^26 + 127*x^25 + 122*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 94*x^20 + 45*x^19 + 84*x^18 + 75*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 23*x^11 + 68*x^10 + 97*x^9 + 54*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 34*x^4 + 107*x^3 + 92*x^2 + 125*x + 54, x^95 + 15*x^93 + 114*x^92 + 69*x^91 + 20*x^90 + 35*x^89 + 22*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 114*x^84 + 57*x^83 + 76*x^82 + 127*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 35*x^75 + 124*x^74 + 85*x^73 + 106*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 30*x^68 + 7*x^67 + 100*x^66 + 97*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 57*x^27 + 36*x^26 + 79*x^25 + 110*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 122*x^20 + 93*x^19 + 60*x^18 + 59*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 71*x^11 + 12*x^10 + 81*x^9 + 34*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 6*x^4 + 123*x^3 + 84*x^2 + 77*x + 98, x^95 + 15*x^93 + 46*x^92 + 69*x^91 + 44*x^90 + 35*x^89 + 74*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 46*x^84 + 57*x^83 + 116*x^82 + 127*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 35*x^75 + 68*x^74 + 85*x^73 + 54*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 66*x^68 + 7*x^67 + 92*x^66 + 97*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 57*x^27 + 28*x^26 + 79*x^25 + 114*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 38*x^20 + 93*x^19 + 4*x^18 + 59*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 71*x^11 + 52*x^10 + 81*x^9 + 126*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 90*x^4 + 123*x^3 + 108*x^2 + 77*x + 62, x^95 + 15*x^93 + 26*x^92 + 117*x^91 + 100*x^90 + 83*x^89 + 110*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 90*x^84 + 73*x^83 + 124*x^82 + 15*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 51*x^75 + 108*x^74 + 101*x^73 + 18*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 118*x^68 + 55*x^67 + 116*x^66 + 17*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 41*x^27 + 52*x^26 + 63*x^25 + 38*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 2*x^20 + 45*x^19 + 44*x^18 + 11*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 23*x^11 + 60*x^10 + 33*x^9 + 42*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 126*x^4 + 107*x^3 + 36*x^2 + 61*x + 42, x^95 + 15*x^93 + 102*x^92 + 37*x^91 + 76*x^90 + 99*x^89 + 98*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 6*x^84 + 89*x^83 + 20*x^82 + 63*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 67*x^75 + 36*x^74 + 21*x^73 + 94*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 106*x^68 + 103*x^67 + 60*x^66 + 33*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 25*x^27 + 60*x^26 + 15*x^25 + 106*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 94*x^20 + 125*x^19 + 36*x^18 + 123*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 103*x^11 + 20*x^10 + 17*x^9 + 6*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 98*x^4 + 91*x^3 + 76*x^2 + 13*x + 102, x^95 + 15*x^93 + 26*x^92 + 53*x^91 + 36*x^90 + 19*x^89 + 46*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 90*x^84 + 9*x^83 + 60*x^82 + 79*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 115*x^75 + 44*x^74 + 37*x^73 + 82*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 118*x^68 + 119*x^67 + 52*x^66 + 81*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 105*x^27 + 116*x^26 + 127*x^25 + 102*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 2*x^20 + 109*x^19 + 108*x^18 + 75*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 87*x^11 + 124*x^10 + 97*x^9 + 106*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 126*x^4 + 43*x^3 + 100*x^2 + 125*x + 106, x^95 + 15*x^93 + 62*x^92 + 117*x^91 + 124*x^90 + 51*x^89 + 74*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 30*x^84 + 73*x^83 + 100*x^82 + 47*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 51*x^75 + 52*x^74 + 5*x^73 + 118*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 18*x^68 + 55*x^67 + 44*x^66 + 113*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 41*x^27 + 44*x^26 + 31*x^25 + 114*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 86*x^20 + 45*x^19 + 52*x^18 + 43*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 23*x^11 + 100*x^10 + 65*x^9 + 62*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 106*x^4 + 107*x^3 + 124*x^2 + 29*x + 94, x^95 + 15*x^93 + 50*x^92 + 85*x^91 + 100*x^90 + 19*x^89 + 70*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 82*x^84 + 105*x^83 + 60*x^82 + 79*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 83*x^75 + 108*x^74 + 37*x^73 + 122*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 126*x^68 + 23*x^67 + 52*x^66 + 81*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 9*x^27 + 52*x^26 + 127*x^25 + 94*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 90*x^20 + 77*x^19 + 108*x^18 + 75*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 55*x^11 + 60*x^10 + 97*x^9 + 114*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 102*x^4 + 75*x^3 + 100*x^2 + 125*x + 82, x^95 + 15*x^93 + 90*x^92 + 85*x^91 + 68*x^90 + 51*x^89 + 14*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 90*x^84 + 105*x^83 + 28*x^82 + 47*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 83*x^75 + 12*x^74 + 5*x^73 + 114*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 118*x^68 + 23*x^67 + 84*x^66 + 113*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 9*x^27 + 20*x^26 + 31*x^25 + 70*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 2*x^20 + 77*x^19 + 76*x^18 + 43*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 55*x^11 + 92*x^10 + 65*x^9 + 10*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 126*x^4 + 75*x^3 + 4*x^2 + 29*x + 74, x^95 + 15*x^93 + 106*x^92 + 85*x^91 + 68*x^90 + 51*x^89 + 94*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 42*x^84 + 105*x^83 + 28*x^82 + 47*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 83*x^75 + 12*x^74 + 5*x^73 + 34*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 38*x^68 + 23*x^67 + 84*x^66 + 113*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 9*x^27 + 20*x^26 + 31*x^25 + 86*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 18*x^20 + 77*x^19 + 76*x^18 + 43*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 55*x^11 + 92*x^10 + 65*x^9 + 122*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 110*x^4 + 75*x^3 + 4*x^2 + 29*x + 122, x^95 + 15*x^93 + 18*x^92 + 101*x^91 + 84*x^90 + 67*x^89 + 54*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 18*x^84 + 25*x^83 + 12*x^82 + 95*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 3*x^75 + 60*x^74 + 53*x^73 + 74*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 126*x^68 + 39*x^67 + 36*x^66 + x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 89*x^27 + 100*x^26 + 111*x^25 + 14*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 26*x^20 + 61*x^19 + 124*x^18 + 27*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 39*x^11 + 76*x^10 + 49*x^9 + 2*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 102*x^4 + 27*x^3 + 20*x^2 + 109*x + 66, x^95 + 15*x^93 + 118*x^92 + 85*x^91 + 92*x^90 + 51*x^89 + 98*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 118*x^84 + 105*x^83 + 68*x^82 + 47*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 83*x^75 + 84*x^74 + 5*x^73 + 30*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 58*x^68 + 23*x^67 + 76*x^66 + 113*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 9*x^27 + 12*x^26 + 31*x^25 + 106*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 14*x^20 + 77*x^19 + 20*x^18 + 43*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 55*x^11 + 4*x^10 + 65*x^9 + 70*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 114*x^4 + 75*x^3 + 28*x^2 + 29*x + 6, x^95 + 15*x^93 + 110*x^92 + 21*x^91 + 60*x^90 + 19*x^89 + 122*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 14*x^84 + 41*x^83 + 36*x^82 + 79*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 19*x^75 + 116*x^74 + 37*x^73 + 70*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 34*x^68 + 87*x^67 + 108*x^66 + 81*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 73*x^27 + 108*x^26 + 127*x^25 + 98*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 6*x^20 + 13*x^19 + 116*x^18 + 75*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 119*x^11 + 36*x^10 + 97*x^9 + 78*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 58*x^4 + 11*x^3 + 60*x^2 + 125*x + 46, x^95 + 15*x^93 + 90*x^92 + 101*x^91 + 116*x^90 + 35*x^89 + 30*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 58*x^84 + 25*x^83 + 44*x^82 + 127*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 3*x^75 + 28*x^74 + 85*x^73 + 34*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 86*x^68 + 39*x^67 + 4*x^66 + 97*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 89*x^27 + 4*x^26 + 79*x^25 + 22*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 98*x^20 + 61*x^19 + 28*x^18 + 59*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 39*x^11 + 44*x^10 + 81*x^9 + 122*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 94*x^4 + 27*x^3 + 116*x^2 + 77*x + 26, x^95 + 15*x^93 + 54*x^92 + 101*x^91 + 108*x^90 + 35*x^89 + 82*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 86*x^84 + 25*x^83 + 116*x^82 + 127*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 3*x^75 + 4*x^74 + 85*x^73 + 110*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 26*x^68 + 39*x^67 + 92*x^66 + 97*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 89*x^27 + 92*x^26 + 79*x^25 + 26*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 110*x^20 + 61*x^19 + 4*x^18 + 59*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 39*x^11 + 116*x^10 + 81*x^9 + 86*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 82*x^4 + 27*x^3 + 108*x^2 + 77*x + 54, x^95 + 15*x^93 + 6*x^92 + 101*x^91 + 108*x^90 + 99*x^89 + 34*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 102*x^84 + 25*x^83 + 116*x^82 + 63*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 3*x^75 + 4*x^74 + 21*x^73 + 30*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 10*x^68 + 39*x^67 + 92*x^66 + 33*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 89*x^27 + 92*x^26 + 15*x^25 + 42*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 62*x^20 + 61*x^19 + 4*x^18 + 123*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 39*x^11 + 116*x^10 + 17*x^9 + 70*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 2*x^4 + 27*x^3 + 108*x^2 + 13*x + 102, x^95 + 15*x^93 + 62*x^92 + 21*x^91 + 60*x^90 + 19*x^89 + 10*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 30*x^84 + 41*x^83 + 36*x^82 + 79*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 19*x^75 + 116*x^74 + 37*x^73 + 54*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 18*x^68 + 87*x^67 + 108*x^66 + 81*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 73*x^27 + 108*x^26 + 127*x^25 + 50*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 86*x^20 + 13*x^19 + 116*x^18 + 75*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 119*x^11 + 36*x^10 + 97*x^9 + 126*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 106*x^4 + 11*x^3 + 60*x^2 + 125*x + 30, x^95 + 15*x^93 + 6*x^92 + 53*x^91 + 28*x^90 + 83*x^89 + 114*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 70*x^84 + 9*x^83 + 4*x^82 + 15*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 115*x^75 + 20*x^74 + 101*x^73 + 14*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 106*x^68 + 119*x^67 + 12*x^66 + 17*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 105*x^27 + 76*x^26 + 63*x^25 + 58*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 30*x^20 + 109*x^19 + 84*x^18 + 11*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 87*x^11 + 68*x^10 + 33*x^9 + 118*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 98*x^4 + 43*x^3 + 92*x^2 + 61*x + 118, x^95 + 15*x^93 + 30*x^92 + 117*x^91 + 28*x^90 + 51*x^89 + 10*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 62*x^84 + 73*x^83 + 68*x^82 + 47*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 51*x^75 + 20*x^74 + 5*x^73 + 54*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 114*x^68 + 55*x^67 + 76*x^66 + 113*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 41*x^27 + 76*x^26 + 31*x^25 + 50*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 118*x^20 + 45*x^19 + 20*x^18 + 43*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 23*x^11 + 68*x^10 + 65*x^9 + 126*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 74*x^4 + 107*x^3 + 28*x^2 + 29*x + 94, x^95 + 15*x^93 + 22*x^92 + 53*x^91 + 92*x^90 + 19*x^89 + 66*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 22*x^84 + 9*x^83 + 68*x^82 + 79*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 115*x^75 + 84*x^74 + 37*x^73 + 62*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 26*x^68 + 119*x^67 + 76*x^66 + 81*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 105*x^27 + 12*x^26 + 127*x^25 + 74*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 46*x^20 + 109*x^19 + 20*x^18 + 75*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 87*x^11 + 4*x^10 + 97*x^9 + 102*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 82*x^4 + 43*x^3 + 28*x^2 + 125*x + 38, x^95 + 15*x^93 + 114*x^92 + 21*x^91 + 4*x^90 + 83*x^89 + 102*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 82*x^84 + 41*x^83 + 28*x^82 + 15*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 19*x^75 + 76*x^74 + 101*x^73 + 90*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 126*x^68 + 87*x^67 + 84*x^66 + 17*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 73*x^27 + 84*x^26 + 63*x^25 + 126*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 90*x^20 + 13*x^19 + 76*x^18 + 11*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 119*x^11 + 28*x^10 + 33*x^9 + 82*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 102*x^4 + 11*x^3 + 4*x^2 + 61*x + 114, x^95 + 15*x^93 + 66*x^92 + 69*x^91 + 116*x^90 + 35*x^89 + 70*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 66*x^84 + 57*x^83 + 108*x^82 + 127*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 35*x^75 + 28*x^74 + 85*x^73 + 58*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 78*x^68 + 7*x^67 + 68*x^66 + 97*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 57*x^27 + 4*x^26 + 79*x^25 + 94*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 10*x^20 + 93*x^19 + 92*x^18 + 59*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 71*x^11 + 44*x^10 + 81*x^9 + 50*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 118*x^4 + 123*x^3 + 52*x^2 + 77*x + 114, x^95 + 15*x^93 + 38*x^92 + 101*x^91 + 108*x^90 + 99*x^89 + 66*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 6*x^84 + 25*x^83 + 116*x^82 + 63*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 3*x^75 + 4*x^74 + 21*x^73 + 126*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 106*x^68 + 39*x^67 + 92*x^66 + 33*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 89*x^27 + 92*x^26 + 15*x^25 + 74*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 94*x^20 + 61*x^19 + 4*x^18 + 123*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 39*x^11 + 116*x^10 + 17*x^9 + 38*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 98*x^4 + 27*x^3 + 108*x^2 + 13*x + 70, x^95 + 15*x^93 + 6*x^92 + 37*x^91 + 108*x^90 + 99*x^89 + 98*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 102*x^84 + 89*x^83 + 116*x^82 + 63*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 67*x^75 + 4*x^74 + 21*x^73 + 94*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 10*x^68 + 103*x^67 + 92*x^66 + 33*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 25*x^27 + 92*x^26 + 15*x^25 + 106*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 62*x^20 + 125*x^19 + 4*x^18 + 123*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 103*x^11 + 116*x^10 + 17*x^9 + 6*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 2*x^4 + 91*x^3 + 108*x^2 + 13*x + 38, x^95 + 15*x^93 + 94*x^92 + 117*x^91 + 124*x^90 + 115*x^89 + 42*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 62*x^84 + 73*x^83 + 100*x^82 + 111*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 51*x^75 + 52*x^74 + 69*x^73 + 22*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 114*x^68 + 55*x^67 + 44*x^66 + 49*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 41*x^27 + 44*x^26 + 95*x^25 + 82*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 118*x^20 + 45*x^19 + 52*x^18 + 107*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 23*x^11 + 100*x^10 + x^9 + 94*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 74*x^4 + 107*x^3 + 124*x^2 + 93*x + 126, x^95 + 15*x^93 + 58*x^92 + 21*x^91 + 100*x^90 + 115*x^89 + 78*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 122*x^84 + 41*x^83 + 124*x^82 + 111*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 19*x^75 + 108*x^74 + 69*x^73 + 50*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 86*x^68 + 87*x^67 + 116*x^66 + 49*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 73*x^27 + 52*x^26 + 95*x^25 + 6*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 34*x^20 + 13*x^19 + 44*x^18 + 107*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 119*x^11 + 60*x^10 + x^9 + 74*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 94*x^4 + 11*x^3 + 36*x^2 + 93*x + 74, x^95 + 15*x^93 + 30*x^92 + 37*x^91 + 44*x^90 + 3*x^89 + 58*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 94*x^84 + 89*x^83 + 116*x^82 + 31*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 67*x^75 + 68*x^74 + 117*x^73 + 70*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 18*x^68 + 103*x^67 + 92*x^66 + 65*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 25*x^27 + 28*x^26 + 47*x^25 + 34*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 22*x^20 + 125*x^19 + 4*x^18 + 91*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 103*x^11 + 52*x^10 + 113*x^9 + 78*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 106*x^4 + 91*x^3 + 108*x^2 + 45*x + 78, x^95 + 15*x^93 + 102*x^92 + 21*x^91 + 124*x^90 + 51*x^89 + 50*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 102*x^84 + 41*x^83 + 36*x^82 + 47*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 19*x^75 + 52*x^74 + 5*x^73 + 78*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 74*x^68 + 87*x^67 + 108*x^66 + 113*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 73*x^27 + 44*x^26 + 31*x^25 + 122*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 62*x^20 + 13*x^19 + 116*x^18 + 43*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 119*x^11 + 100*x^10 + 65*x^9 + 54*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 66*x^4 + 11*x^3 + 60*x^2 + 29*x + 118, x^95 + 15*x^93 + 122*x^92 + 53*x^91 + 100*x^90 + 19*x^89 + 78*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 58*x^84 + 9*x^83 + 124*x^82 + 79*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 115*x^75 + 108*x^74 + 37*x^73 + 50*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 22*x^68 + 119*x^67 + 116*x^66 + 81*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 105*x^27 + 52*x^26 + 127*x^25 + 6*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 98*x^20 + 109*x^19 + 44*x^18 + 75*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 87*x^11 + 60*x^10 + 97*x^9 + 74*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 30*x^4 + 43*x^3 + 36*x^2 + 125*x + 74, x^95 + 15*x^93 + 118*x^92 + 69*x^91 + 12*x^90 + 3*x^89 + 50*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 86*x^84 + 57*x^83 + 84*x^82 + 31*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 35*x^75 + 100*x^74 + 117*x^73 + 14*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 26*x^68 + 7*x^67 + 124*x^66 + 65*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 57*x^27 + 124*x^26 + 47*x^25 + 122*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 110*x^20 + 93*x^19 + 100*x^18 + 91*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 71*x^11 + 84*x^10 + 113*x^9 + 118*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 82*x^4 + 123*x^3 + 12*x^2 + 45*x + 22, x^95 + 15*x^93 + 106*x^92 + 53*x^91 + 68*x^90 + 83*x^89 + 94*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 42*x^84 + 9*x^83 + 28*x^82 + 15*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 115*x^75 + 12*x^74 + 101*x^73 + 34*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 38*x^68 + 119*x^67 + 84*x^66 + 17*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 105*x^27 + 20*x^26 + 63*x^25 + 86*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 18*x^20 + 109*x^19 + 76*x^18 + 11*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 87*x^11 + 92*x^10 + 33*x^9 + 122*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 110*x^4 + 43*x^3 + 4*x^2 + 61*x + 122, x^95 + 15*x^93 + 54*x^92 + 21*x^91 + 124*x^90 + 115*x^89 + 2*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 118*x^84 + 41*x^83 + 36*x^82 + 111*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 19*x^75 + 52*x^74 + 69*x^73 + 126*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 58*x^68 + 87*x^67 + 108*x^66 + 49*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 73*x^27 + 44*x^26 + 95*x^25 + 10*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 14*x^20 + 13*x^19 + 116*x^18 + 107*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 119*x^11 + 100*x^10 + x^9 + 38*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 114*x^4 + 11*x^3 + 60*x^2 + 93*x + 38, x^95 + 15*x^93 + 74*x^92 + 37*x^91 + 52*x^90 + 35*x^89 + 78*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 106*x^84 + 89*x^83 + 108*x^82 + 127*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 67*x^75 + 92*x^74 + 85*x^73 + 114*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 38*x^68 + 103*x^67 + 68*x^66 + 97*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 25*x^27 + 68*x^26 + 79*x^25 + 6*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 82*x^20 + 125*x^19 + 92*x^18 + 59*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 103*x^11 + 108*x^10 + 81*x^9 + 10*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 110*x^4 + 91*x^3 + 52*x^2 + 77*x + 106, x^95 + 15*x^93 + 122*x^92 + 85*x^91 + 100*x^90 + 51*x^89 + 14*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 58*x^84 + 105*x^83 + 124*x^82 + 47*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 83*x^75 + 108*x^74 + 5*x^73 + 114*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 22*x^68 + 23*x^67 + 116*x^66 + 113*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 9*x^27 + 52*x^26 + 31*x^25 + 70*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 98*x^20 + 77*x^19 + 44*x^18 + 43*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 55*x^11 + 60*x^10 + 65*x^9 + 10*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 30*x^4 + 75*x^3 + 36*x^2 + 29*x + 10, x^95 + 15*x^93 + 78*x^92 + 21*x^91 + 60*x^90 + 19*x^89 + 90*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 110*x^84 + 41*x^83 + 36*x^82 + 79*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 19*x^75 + 116*x^74 + 37*x^73 + 102*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 66*x^68 + 87*x^67 + 108*x^66 + 81*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 73*x^27 + 108*x^26 + 127*x^25 + 66*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 102*x^20 + 13*x^19 + 116*x^18 + 75*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 119*x^11 + 36*x^10 + 97*x^9 + 110*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 90*x^4 + 11*x^3 + 60*x^2 + 125*x + 78, x^95 + 15*x^93 + 118*x^92 + 37*x^91 + 44*x^90 + 35*x^89 + 18*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 22*x^84 + 89*x^83 + 52*x^82 + 127*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 67*x^75 + 68*x^74 + 85*x^73 + 46*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 90*x^68 + 103*x^67 + 28*x^66 + 97*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 25*x^27 + 28*x^26 + 79*x^25 + 90*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 46*x^20 + 125*x^19 + 68*x^18 + 59*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 103*x^11 + 52*x^10 + 81*x^9 + 22*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 18*x^4 + 91*x^3 + 44*x^2 + 77*x + 118, x^95 + 15*x^93 + 126*x^92 + 5*x^91 + 76*x^90 + 35*x^89 + 122*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 126*x^84 + 121*x^83 + 84*x^82 + 127*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 99*x^75 + 36*x^74 + 85*x^73 + 6*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 114*x^68 + 71*x^67 + 124*x^66 + 97*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 121*x^27 + 60*x^26 + 79*x^25 + 98*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 54*x^20 + 29*x^19 + 100*x^18 + 59*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 7*x^11 + 20*x^10 + 81*x^9 + 14*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 74*x^4 + 59*x^3 + 12*x^2 + 77*x + 78, x^95 + 15*x^93 + 66*x^92 + 117*x^91 + 100*x^90 + 115*x^89 + 22*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 34*x^84 + 73*x^83 + 60*x^82 + 111*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 51*x^75 + 108*x^74 + 69*x^73 + 42*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 46*x^68 + 55*x^67 + 52*x^66 + 49*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 41*x^27 + 52*x^26 + 95*x^25 + 110*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 106*x^20 + 45*x^19 + 108*x^18 + 107*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 23*x^11 + 60*x^10 + x^9 + 98*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 86*x^4 + 107*x^3 + 100*x^2 + 93*x + 2, x^95 + 15*x^93 + 14*x^92 + 69*x^91 + 12*x^90 + 35*x^89 + 74*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 78*x^84 + 57*x^83 + 20*x^82 + 127*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 35*x^75 + 100*x^74 + 85*x^73 + 54*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 34*x^68 + 7*x^67 + 60*x^66 + 97*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 57*x^27 + 124*x^26 + 79*x^25 + 114*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 70*x^20 + 93*x^19 + 36*x^18 + 59*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 71*x^11 + 84*x^10 + 81*x^9 + 126*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 58*x^4 + 123*x^3 + 76*x^2 + 77*x + 126, x^95 + 15*x^93 + 106*x^92 + 5*x^91 + 116*x^90 + 67*x^89 + 46*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 10*x^84 + 121*x^83 + 44*x^82 + 95*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 99*x^75 + 28*x^74 + 53*x^73 + 18*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 6*x^68 + 71*x^67 + 4*x^66 + x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 121*x^27 + 4*x^26 + 111*x^25 + 102*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 114*x^20 + 29*x^19 + 28*x^18 + 27*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 7*x^11 + 44*x^10 + 49*x^9 + 42*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 78*x^4 + 59*x^3 + 116*x^2 + 109*x + 10, x^95 + 15*x^93 + 6*x^92 + 53*x^91 + 60*x^90 + 19*x^89 + 18*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 6*x^84 + 9*x^83 + 100*x^82 + 79*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 115*x^75 + 116*x^74 + 37*x^73 + 110*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 42*x^68 + 119*x^67 + 44*x^66 + 81*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 105*x^27 + 108*x^26 + 127*x^25 + 90*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 94*x^20 + 109*x^19 + 52*x^18 + 75*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 87*x^11 + 36*x^10 + 97*x^9 + 86*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 34*x^4 + 43*x^3 + 124*x^2 + 125*x + 22, x^95 + 15*x^93 + 54*x^92 + 5*x^91 + 44*x^90 + 67*x^89 + 82*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 86*x^84 + 121*x^83 + 52*x^82 + 95*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 99*x^75 + 68*x^74 + 53*x^73 + 110*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 26*x^68 + 71*x^67 + 28*x^66 + x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 121*x^27 + 28*x^26 + 111*x^25 + 26*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 110*x^20 + 29*x^19 + 68*x^18 + 27*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 7*x^11 + 52*x^10 + 49*x^9 + 86*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 82*x^4 + 59*x^3 + 44*x^2 + 109*x + 54, x^95 + 15*x^93 + 50*x^92 + 85*x^91 + 100*x^90 + 83*x^89 + 6*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 82*x^84 + 105*x^83 + 60*x^82 + 15*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 83*x^75 + 108*x^74 + 101*x^73 + 58*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 126*x^68 + 23*x^67 + 52*x^66 + 17*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 9*x^27 + 52*x^26 + 63*x^25 + 30*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 90*x^20 + 77*x^19 + 108*x^18 + 11*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 55*x^11 + 60*x^10 + 33*x^9 + 50*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 102*x^4 + 75*x^3 + 100*x^2 + 61*x + 18, x^95 + 15*x^93 + 118*x^92 + 101*x^91 + 76*x^90 + 99*x^89 + 114*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 86*x^84 + 25*x^83 + 20*x^82 + 63*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 3*x^75 + 36*x^74 + 21*x^73 + 78*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 26*x^68 + 39*x^67 + 60*x^66 + 33*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 89*x^27 + 60*x^26 + 15*x^25 + 58*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 110*x^20 + 61*x^19 + 36*x^18 + 123*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 39*x^11 + 20*x^10 + 17*x^9 + 54*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 82*x^4 + 27*x^3 + 76*x^2 + 13*x + 86, x^95 + 15*x^93 + 46*x^92 + 37*x^91 + 108*x^90 + 67*x^89 + 10*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 46*x^84 + 89*x^83 + 52*x^82 + 95*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 67*x^75 + 4*x^74 + 53*x^73 + 118*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 66*x^68 + 103*x^67 + 28*x^66 + x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 25*x^27 + 92*x^26 + 111*x^25 + 50*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 38*x^20 + 125*x^19 + 68*x^18 + 27*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 103*x^11 + 116*x^10 + 49*x^9 + 62*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 90*x^4 + 91*x^3 + 44*x^2 + 109*x + 126, x^95 + 15*x^93 + 38*x^92 + 53*x^91 + 92*x^90 + 83*x^89 + 82*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 102*x^84 + 9*x^83 + 68*x^82 + 15*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 115*x^75 + 84*x^74 + 101*x^73 + 46*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 74*x^68 + 119*x^67 + 76*x^66 + 17*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 105*x^27 + 12*x^26 + 63*x^25 + 26*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 62*x^20 + 109*x^19 + 20*x^18 + 11*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 87*x^11 + 4*x^10 + 33*x^9 + 22*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 66*x^4 + 43*x^3 + 28*x^2 + 61*x + 22, x^95 + 15*x^93 + 42*x^92 + 117*x^91 + 100*x^90 + 83*x^89 + 62*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 42*x^84 + 73*x^83 + 124*x^82 + 15*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 51*x^75 + 108*x^74 + 101*x^73 + 66*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 38*x^68 + 55*x^67 + 116*x^66 + 17*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 41*x^27 + 52*x^26 + 63*x^25 + 54*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 18*x^20 + 45*x^19 + 44*x^18 + 11*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 23*x^11 + 60*x^10 + 33*x^9 + 26*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 110*x^4 + 107*x^3 + 36*x^2 + 61*x + 90, x^95 + 15*x^93 + 70*x^92 + 85*x^91 + 92*x^90 + 51*x^89 + 114*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 6*x^84 + 105*x^83 + 68*x^82 + 47*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 83*x^75 + 84*x^74 + 5*x^73 + 14*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 42*x^68 + 23*x^67 + 76*x^66 + 113*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 9*x^27 + 12*x^26 + 31*x^25 + 58*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 94*x^20 + 77*x^19 + 20*x^18 + 43*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 55*x^11 + 4*x^10 + 65*x^9 + 118*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 34*x^4 + 75*x^3 + 28*x^2 + 29*x + 118, x^95 + 15*x^93 + 54*x^92 + 53*x^91 + 60*x^90 + 19*x^89 + 2*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 118*x^84 + 9*x^83 + 100*x^82 + 79*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 115*x^75 + 116*x^74 + 37*x^73 + 126*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 58*x^68 + 119*x^67 + 44*x^66 + 81*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 105*x^27 + 108*x^26 + 127*x^25 + 10*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 14*x^20 + 109*x^19 + 52*x^18 + 75*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 87*x^11 + 36*x^10 + 97*x^9 + 38*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 114*x^4 + 43*x^3 + 124*x^2 + 125*x + 38, x^95 + 15*x^93 + 102*x^92 + 37*x^91 + 108*x^90 + 35*x^89 + 2*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 70*x^84 + 89*x^83 + 116*x^82 + 127*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 67*x^75 + 4*x^74 + 85*x^73 + 62*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 42*x^68 + 103*x^67 + 92*x^66 + 97*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 25*x^27 + 92*x^26 + 79*x^25 + 10*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 30*x^20 + 125*x^19 + 4*x^18 + 59*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 103*x^11 + 116*x^10 + 81*x^9 + 102*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 34*x^4 + 91*x^3 + 108*x^2 + 77*x + 6, x^95 + 15*x^93 + 82*x^92 + 5*x^91 + 84*x^90 + 35*x^89 + 118*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 82*x^84 + 121*x^83 + 12*x^82 + 127*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 99*x^75 + 60*x^74 + 85*x^73 + 10*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 62*x^68 + 71*x^67 + 36*x^66 + 97*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 121*x^27 + 100*x^26 + 79*x^25 + 78*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 90*x^20 + 29*x^19 + 124*x^18 + 59*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 7*x^11 + 76*x^10 + 81*x^9 + 66*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 38*x^4 + 59*x^3 + 20*x^2 + 77*x + 2, x^95 + 15*x^93 + 62*x^92 + 5*x^91 + 12*x^90 + 99*x^89 + 58*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 62*x^84 + 121*x^83 + 20*x^82 + 63*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 99*x^75 + 100*x^74 + 21*x^73 + 70*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 50*x^68 + 71*x^67 + 60*x^66 + 33*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 121*x^27 + 124*x^26 + 15*x^25 + 34*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 118*x^20 + 29*x^19 + 36*x^18 + 123*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 7*x^11 + 84*x^10 + 17*x^9 + 78*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 10*x^4 + 59*x^3 + 76*x^2 + 13*x + 14, x^95 + 15*x^93 + 58*x^92 + 53*x^91 + 68*x^90 + 83*x^89 + 110*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 58*x^84 + 9*x^83 + 28*x^82 + 15*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 115*x^75 + 12*x^74 + 101*x^73 + 18*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 22*x^68 + 119*x^67 + 84*x^66 + 17*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 105*x^27 + 20*x^26 + 63*x^25 + 38*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 98*x^20 + 109*x^19 + 76*x^18 + 11*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 87*x^11 + 92*x^10 + 33*x^9 + 42*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 30*x^4 + 43*x^3 + 4*x^2 + 61*x + 106, x^95 + 15*x^93 + 6*x^92 + 53*x^91 + 92*x^90 + 83*x^89 + 50*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 70*x^84 + 9*x^83 + 68*x^82 + 15*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 115*x^75 + 84*x^74 + 101*x^73 + 78*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 106*x^68 + 119*x^67 + 76*x^66 + 17*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 105*x^27 + 12*x^26 + 63*x^25 + 122*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 30*x^20 + 109*x^19 + 20*x^18 + 11*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 87*x^11 + 4*x^10 + 33*x^9 + 54*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 98*x^4 + 43*x^3 + 28*x^2 + 61*x + 54, x^95 + 15*x^93 + 46*x^92 + 5*x^91 + 44*x^90 + 35*x^89 + 10*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 46*x^84 + 121*x^83 + 116*x^82 + 127*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 99*x^75 + 68*x^74 + 85*x^73 + 118*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 66*x^68 + 71*x^67 + 92*x^66 + 97*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 121*x^27 + 28*x^26 + 79*x^25 + 50*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 38*x^20 + 29*x^19 + 4*x^18 + 59*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 7*x^11 + 52*x^10 + 81*x^9 + 62*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 90*x^4 + 59*x^3 + 108*x^2 + 77*x + 126, x^95 + 15*x^93 + 58*x^92 + 5*x^91 + 84*x^90 + 67*x^89 + 94*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 90*x^84 + 121*x^83 + 76*x^82 + 95*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 99*x^75 + 60*x^74 + 53*x^73 + 98*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 54*x^68 + 71*x^67 + 100*x^66 + x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 121*x^27 + 100*x^26 + 111*x^25 + 86*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 2*x^20 + 29*x^19 + 60*x^18 + 27*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 7*x^11 + 76*x^10 + 49*x^9 + 58*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 62*x^4 + 59*x^3 + 84*x^2 + 109*x + 26, x^95 + 15*x^93 + 6*x^92 + 85*x^91 + 28*x^90 + 115*x^89 + 50*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 70*x^84 + 105*x^83 + 4*x^82 + 111*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 83*x^75 + 20*x^74 + 69*x^73 + 78*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 106*x^68 + 23*x^67 + 12*x^66 + 49*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 9*x^27 + 76*x^26 + 95*x^25 + 122*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 30*x^20 + 77*x^19 + 84*x^18 + 107*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 55*x^11 + 68*x^10 + x^9 + 54*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 98*x^4 + 75*x^3 + 92*x^2 + 93*x + 54, x^95 + 15*x^93 + 46*x^92 + 5*x^91 + 12*x^90 + 99*x^89 + 106*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 110*x^84 + 121*x^83 + 20*x^82 + 63*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 99*x^75 + 100*x^74 + 21*x^73 + 22*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 2*x^68 + 71*x^67 + 60*x^66 + 33*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 121*x^27 + 124*x^26 + 15*x^25 + 18*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 102*x^20 + 29*x^19 + 36*x^18 + 123*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 7*x^11 + 84*x^10 + 17*x^9 + 94*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 26*x^4 + 59*x^3 + 76*x^2 + 13*x + 94, x^95 + 15*x^93 + 18*x^92 + 85*x^91 + 100*x^90 + 19*x^89 + 38*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 50*x^84 + 105*x^83 + 60*x^82 + 79*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 83*x^75 + 108*x^74 + 37*x^73 + 26*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 30*x^68 + 23*x^67 + 52*x^66 + 81*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 9*x^27 + 52*x^26 + 127*x^25 + 62*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 58*x^20 + 77*x^19 + 108*x^18 + 75*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 55*x^11 + 60*x^10 + 97*x^9 + 18*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 6*x^4 + 75*x^3 + 100*x^2 + 125*x + 114, x^95 + 15*x^93 + 102*x^92 + 85*x^91 + 28*x^90 + 115*x^89 + 18*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 38*x^84 + 105*x^83 + 4*x^82 + 111*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 83*x^75 + 20*x^74 + 69*x^73 + 110*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 10*x^68 + 23*x^67 + 12*x^66 + 49*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 9*x^27 + 76*x^26 + 95*x^25 + 90*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 126*x^20 + 77*x^19 + 84*x^18 + 107*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 55*x^11 + 68*x^10 + x^9 + 86*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 2*x^4 + 75*x^3 + 92*x^2 + 93*x + 86, x^95 + 15*x^93 + 50*x^92 + 21*x^91 + 100*x^90 + 19*x^89 + 6*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 82*x^84 + 41*x^83 + 60*x^82 + 79*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 19*x^75 + 108*x^74 + 37*x^73 + 58*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 126*x^68 + 87*x^67 + 52*x^66 + 81*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 73*x^27 + 52*x^26 + 127*x^25 + 30*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 90*x^20 + 13*x^19 + 108*x^18 + 75*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 119*x^11 + 60*x^10 + 97*x^9 + 50*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 102*x^4 + 11*x^3 + 100*x^2 + 125*x + 18, x^95 + 15*x^93 + 26*x^92 + 53*x^91 + 100*x^90 + 19*x^89 + 110*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 90*x^84 + 9*x^83 + 124*x^82 + 79*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 115*x^75 + 108*x^74 + 37*x^73 + 18*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 118*x^68 + 119*x^67 + 116*x^66 + 81*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 105*x^27 + 52*x^26 + 127*x^25 + 38*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 2*x^20 + 109*x^19 + 44*x^18 + 75*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 87*x^11 + 60*x^10 + 97*x^9 + 42*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 126*x^4 + 43*x^3 + 36*x^2 + 125*x + 42, x^95 + 15*x^93 + 42*x^92 + 53*x^91 + 4*x^90 + 83*x^89 + 94*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 106*x^84 + 9*x^83 + 92*x^82 + 15*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 115*x^75 + 76*x^74 + 101*x^73 + 34*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 102*x^68 + 119*x^67 + 20*x^66 + 17*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 105*x^27 + 84*x^26 + 63*x^25 + 86*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 82*x^20 + 109*x^19 + 12*x^18 + 11*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 87*x^11 + 28*x^10 + 33*x^9 + 122*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 46*x^4 + 43*x^3 + 68*x^2 + 61*x + 122, x^95 + 15*x^93 + 70*x^92 + 101*x^91 + 76*x^90 + 35*x^89 + 66*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 102*x^84 + 25*x^83 + 20*x^82 + 127*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 3*x^75 + 36*x^74 + 85*x^73 + 126*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 10*x^68 + 39*x^67 + 60*x^66 + 97*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 89*x^27 + 60*x^26 + 79*x^25 + 74*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 62*x^20 + 61*x^19 + 36*x^18 + 59*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 39*x^11 + 20*x^10 + 81*x^9 + 38*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 2*x^4 + 27*x^3 + 76*x^2 + 77*x + 6, x^95 + 15*x^93 + 50*x^92 + 21*x^91 + 68*x^90 + 83*x^89 + 102*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 18*x^84 + 41*x^83 + 92*x^82 + 15*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 19*x^75 + 12*x^74 + 101*x^73 + 90*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 62*x^68 + 87*x^67 + 20*x^66 + 17*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 73*x^27 + 20*x^26 + 63*x^25 + 126*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 26*x^20 + 13*x^19 + 12*x^18 + 11*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 119*x^11 + 92*x^10 + 33*x^9 + 82*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 38*x^4 + 11*x^3 + 68*x^2 + 61*x + 114, x^95 + 15*x^93 + 98*x^92 + 37*x^91 + 52*x^90 + 3*x^89 + 102*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 98*x^84 + 89*x^83 + 44*x^82 + 31*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 67*x^75 + 92*x^74 + 117*x^73 + 26*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 46*x^68 + 103*x^67 + 4*x^66 + 65*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 25*x^27 + 68*x^26 + 47*x^25 + 126*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 42*x^20 + 125*x^19 + 28*x^18 + 91*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 103*x^11 + 108*x^10 + 113*x^9 + 18*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 86*x^4 + 91*x^3 + 116*x^2 + 45*x + 82, x^95 + 15*x^93 + 38*x^92 + 85*x^91 + 60*x^90 + 115*x^89 + 50*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 38*x^84 + 105*x^83 + 100*x^82 + 111*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 83*x^75 + 116*x^74 + 69*x^73 + 78*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 10*x^68 + 23*x^67 + 44*x^66 + 49*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 9*x^27 + 108*x^26 + 95*x^25 + 122*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 126*x^20 + 77*x^19 + 52*x^18 + 107*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 55*x^11 + 36*x^10 + x^9 + 54*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 2*x^4 + 75*x^3 + 124*x^2 + 93*x + 118, x^95 + 15*x^93 + 34*x^92 + 21*x^91 + 100*x^90 + 83*x^89 + 118*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 2*x^84 + 41*x^83 + 60*x^82 + 15*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 19*x^75 + 108*x^74 + 101*x^73 + 74*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 78*x^68 + 87*x^67 + 52*x^66 + 17*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 73*x^27 + 52*x^26 + 63*x^25 + 78*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 74*x^20 + 13*x^19 + 108*x^18 + 11*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 119*x^11 + 60*x^10 + 33*x^9 + 2*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 118*x^4 + 11*x^3 + 100*x^2 + 61*x + 34, x^95 + 15*x^93 + 86*x^92 + 21*x^91 + 124*x^90 + 51*x^89 + 98*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 22*x^84 + 41*x^83 + 36*x^82 + 47*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 19*x^75 + 52*x^74 + 5*x^73 + 30*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 26*x^68 + 87*x^67 + 108*x^66 + 113*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 73*x^27 + 44*x^26 + 31*x^25 + 106*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 46*x^20 + 13*x^19 + 116*x^18 + 43*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 119*x^11 + 100*x^10 + 65*x^9 + 70*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 82*x^4 + 11*x^3 + 60*x^2 + 29*x + 70, x^95 + 15*x^93 + 86*x^92 + 37*x^91 + 76*x^90 + 35*x^89 + 82*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 54*x^84 + 89*x^83 + 20*x^82 + 127*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 67*x^75 + 36*x^74 + 85*x^73 + 110*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 58*x^68 + 103*x^67 + 60*x^66 + 97*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 25*x^27 + 60*x^26 + 79*x^25 + 26*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 78*x^20 + 125*x^19 + 36*x^18 + 59*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 103*x^11 + 20*x^10 + 81*x^9 + 86*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 114*x^4 + 91*x^3 + 76*x^2 + 77*x + 118, x^95 + 15*x^93 + 126*x^92 + 85*x^91 + 124*x^90 + 83*x^89 + 10*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 94*x^84 + 105*x^83 + 100*x^82 + 15*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 83*x^75 + 52*x^74 + 101*x^73 + 54*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 82*x^68 + 23*x^67 + 44*x^66 + 17*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 9*x^27 + 44*x^26 + 63*x^25 + 50*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 22*x^20 + 77*x^19 + 52*x^18 + 11*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 55*x^11 + 100*x^10 + 33*x^9 + 126*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 42*x^4 + 75*x^3 + 124*x^2 + 61*x + 30, x^95 + 15*x^93 + 2*x^92 + 69*x^91 + 52*x^90 + 99*x^89 + 6*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 2*x^84 + 57*x^83 + 44*x^82 + 63*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 35*x^75 + 92*x^74 + 21*x^73 + 122*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 14*x^68 + 7*x^67 + 4*x^66 + 33*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 57*x^27 + 68*x^26 + 15*x^25 + 30*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 74*x^20 + 93*x^19 + 28*x^18 + 123*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 71*x^11 + 108*x^10 + 17*x^9 + 114*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 54*x^4 + 123*x^3 + 116*x^2 + 13*x + 50, x^95 + 15*x^93 + 94*x^92 + 101*x^91 + 12*x^90 + 67*x^89 + 26*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 94*x^84 + 25*x^83 + 20*x^82 + 95*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 3*x^75 + 100*x^74 + 53*x^73 + 102*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 18*x^68 + 39*x^67 + 60*x^66 + x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 89*x^27 + 124*x^26 + 111*x^25 + 2*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 22*x^20 + 61*x^19 + 36*x^18 + 27*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 39*x^11 + 84*x^10 + 49*x^9 + 110*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 106*x^4 + 27*x^3 + 76*x^2 + 109*x + 46, x^95 + 15*x^93 + 30*x^92 + 5*x^91 + 76*x^90 + 99*x^89 + 90*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 30*x^84 + 121*x^83 + 84*x^82 + 63*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 99*x^75 + 36*x^74 + 21*x^73 + 38*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 82*x^68 + 71*x^67 + 124*x^66 + 33*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 121*x^27 + 60*x^26 + 15*x^25 + 66*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 86*x^20 + 29*x^19 + 100*x^18 + 123*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 7*x^11 + 20*x^10 + 17*x^9 + 46*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 42*x^4 + 59*x^3 + 12*x^2 + 13*x + 110, x^95 + 15*x^93 + 70*x^92 + 101*x^91 + 76*x^90 + 99*x^89 + 2*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 102*x^84 + 25*x^83 + 20*x^82 + 63*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 3*x^75 + 36*x^74 + 21*x^73 + 62*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 10*x^68 + 39*x^67 + 60*x^66 + 33*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 89*x^27 + 60*x^26 + 15*x^25 + 10*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 62*x^20 + 61*x^19 + 36*x^18 + 123*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 39*x^11 + 20*x^10 + 17*x^9 + 102*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 2*x^4 + 27*x^3 + 76*x^2 + 13*x + 70, x^95 + 15*x^93 + 54*x^92 + 101*x^91 + 76*x^90 + 99*x^89 + 50*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 22*x^84 + 25*x^83 + 20*x^82 + 63*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 3*x^75 + 36*x^74 + 21*x^73 + 14*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 90*x^68 + 39*x^67 + 60*x^66 + 33*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 89*x^27 + 60*x^26 + 15*x^25 + 122*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 46*x^20 + 61*x^19 + 36*x^18 + 123*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 39*x^11 + 20*x^10 + 17*x^9 + 118*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 18*x^4 + 27*x^3 + 76*x^2 + 13*x + 22, x^95 + 15*x^93 + 22*x^92 + 37*x^91 + 12*x^90 + 35*x^89 + 82*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 118*x^84 + 89*x^83 + 84*x^82 + 127*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 67*x^75 + 100*x^74 + 85*x^73 + 110*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 122*x^68 + 103*x^67 + 124*x^66 + 97*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 25*x^27 + 124*x^26 + 79*x^25 + 26*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 14*x^20 + 125*x^19 + 100*x^18 + 59*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 103*x^11 + 84*x^10 + 81*x^9 + 86*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 50*x^4 + 91*x^3 + 12*x^2 + 77*x + 118, x^95 + 15*x^93 + 10*x^92 + 5*x^91 + 20*x^90 + 3*x^89 + 110*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 106*x^84 + 121*x^83 + 12*x^82 + 31*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 99*x^75 + 124*x^74 + 117*x^73 + 82*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 38*x^68 + 71*x^67 + 36*x^66 + 65*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 121*x^27 + 36*x^26 + 47*x^25 + 38*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 82*x^20 + 29*x^19 + 124*x^18 + 91*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 7*x^11 + 12*x^10 + 113*x^9 + 106*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 110*x^4 + 59*x^3 + 20*x^2 + 45*x + 10, x^95 + 15*x^93 + 6*x^92 + 69*x^91 + 108*x^90 + 3*x^89 + 34*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 102*x^84 + 57*x^83 + 116*x^82 + 31*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 35*x^75 + 4*x^74 + 117*x^73 + 30*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 10*x^68 + 7*x^67 + 92*x^66 + 65*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 57*x^27 + 92*x^26 + 47*x^25 + 42*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 62*x^20 + 93*x^19 + 4*x^18 + 91*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 71*x^11 + 116*x^10 + 113*x^9 + 70*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 2*x^4 + 123*x^3 + 108*x^2 + 45*x + 102, x^95 + 15*x^93 + 102*x^92 + 69*x^91 + 76*x^90 + 67*x^89 + 98*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 6*x^84 + 57*x^83 + 20*x^82 + 95*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 35*x^75 + 36*x^74 + 53*x^73 + 94*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 106*x^68 + 7*x^67 + 60*x^66 + x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 57*x^27 + 60*x^26 + 111*x^25 + 106*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 94*x^20 + 93*x^19 + 36*x^18 + 27*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 71*x^11 + 20*x^10 + 49*x^9 + 6*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 98*x^4 + 123*x^3 + 76*x^2 + 109*x + 102, x^95 + 15*x^93 + 90*x^92 + 5*x^91 + 52*x^90 + 67*x^89 + 30*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 58*x^84 + 121*x^83 + 108*x^82 + 95*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 99*x^75 + 92*x^74 + 53*x^73 + 34*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 86*x^68 + 71*x^67 + 68*x^66 + x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 121*x^27 + 68*x^26 + 111*x^25 + 22*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 98*x^20 + 29*x^19 + 92*x^18 + 27*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 7*x^11 + 108*x^10 + 49*x^9 + 122*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 94*x^4 + 59*x^3 + 52*x^2 + 109*x + 26, x^95 + 15*x^93 + 58*x^92 + 101*x^91 + 116*x^90 + 35*x^89 + 126*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 26*x^84 + 25*x^83 + 44*x^82 + 127*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 3*x^75 + 28*x^74 + 85*x^73 + 66*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 118*x^68 + 39*x^67 + 4*x^66 + 97*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 89*x^27 + 4*x^26 + 79*x^25 + 118*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 66*x^20 + 61*x^19 + 28*x^18 + 59*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 39*x^11 + 44*x^10 + 81*x^9 + 26*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 126*x^4 + 27*x^3 + 116*x^2 + 77*x + 58, x^95 + 15*x^93 + 118*x^92 + 53*x^91 + 92*x^90 + 19*x^89 + 34*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 118*x^84 + 9*x^83 + 68*x^82 + 79*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 115*x^75 + 84*x^74 + 37*x^73 + 94*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 58*x^68 + 119*x^67 + 76*x^66 + 81*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 105*x^27 + 12*x^26 + 127*x^25 + 42*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 14*x^20 + 109*x^19 + 20*x^18 + 75*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 87*x^11 + 4*x^10 + 97*x^9 + 6*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 114*x^4 + 43*x^3 + 28*x^2 + 125*x + 70, x^95 + 15*x^93 + 114*x^92 + 53*x^91 + 100*x^90 + 115*x^89 + 70*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 18*x^84 + 9*x^83 + 60*x^82 + 111*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 115*x^75 + 108*x^74 + 69*x^73 + 122*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 62*x^68 + 119*x^67 + 52*x^66 + 49*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 105*x^27 + 52*x^26 + 95*x^25 + 94*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 26*x^20 + 109*x^19 + 108*x^18 + 107*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 87*x^11 + 60*x^10 + x^9 + 114*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 38*x^4 + 43*x^3 + 100*x^2 + 93*x + 82, x^95 + 15*x^93 + 82*x^92 + 37*x^91 + 20*x^90 + 3*x^89 + 54*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 82*x^84 + 89*x^83 + 76*x^82 + 31*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 67*x^75 + 124*x^74 + 117*x^73 + 74*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 62*x^68 + 103*x^67 + 100*x^66 + 65*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 25*x^27 + 36*x^26 + 47*x^25 + 14*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 90*x^20 + 125*x^19 + 60*x^18 + 91*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 103*x^11 + 12*x^10 + 113*x^9 + 2*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 38*x^4 + 91*x^3 + 84*x^2 + 45*x + 66, x^95 + 15*x^93 + 102*x^92 + 69*x^91 + 12*x^90 + 67*x^89 + 34*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 6*x^84 + 57*x^83 + 84*x^82 + 95*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 35*x^75 + 100*x^74 + 53*x^73 + 30*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 106*x^68 + 7*x^67 + 124*x^66 + x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 57*x^27 + 124*x^26 + 111*x^25 + 42*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 94*x^20 + 93*x^19 + 100*x^18 + 27*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 71*x^11 + 84*x^10 + 49*x^9 + 70*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 98*x^4 + 123*x^3 + 12*x^2 + 109*x + 38, x^95 + 15*x^93 + 34*x^92 + 53*x^91 + 100*x^90 + 115*x^89 + 54*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 2*x^84 + 9*x^83 + 60*x^82 + 111*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 115*x^75 + 108*x^74 + 69*x^73 + 10*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 78*x^68 + 119*x^67 + 52*x^66 + 49*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 105*x^27 + 52*x^26 + 95*x^25 + 14*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 74*x^20 + 109*x^19 + 108*x^18 + 107*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 87*x^11 + 60*x^10 + x^9 + 66*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 118*x^4 + 43*x^3 + 100*x^2 + 93*x + 98, x^95 + 15*x^93 + 26*x^92 + 21*x^91 + 36*x^90 + 51*x^89 + 46*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 90*x^84 + 41*x^83 + 60*x^82 + 47*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 19*x^75 + 44*x^74 + 5*x^73 + 82*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 118*x^68 + 87*x^67 + 52*x^66 + 113*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 73*x^27 + 116*x^26 + 31*x^25 + 102*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 2*x^20 + 13*x^19 + 108*x^18 + 43*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 119*x^11 + 124*x^10 + 65*x^9 + 106*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 126*x^4 + 11*x^3 + 100*x^2 + 29*x + 106, x^95 + 15*x^93 + 106*x^92 + 101*x^91 + 84*x^90 + 35*x^89 + 14*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 74*x^84 + 25*x^83 + 76*x^82 + 127*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 3*x^75 + 60*x^74 + 85*x^73 + 50*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 70*x^68 + 39*x^67 + 100*x^66 + 97*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 89*x^27 + 100*x^26 + 79*x^25 + 70*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 50*x^20 + 61*x^19 + 60*x^18 + 59*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 39*x^11 + 76*x^10 + 81*x^9 + 74*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 14*x^4 + 27*x^3 + 84*x^2 + 77*x + 106, x^95 + 15*x^93 + 62*x^92 + 53*x^91 + 92*x^90 + 115*x^89 + 106*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 94*x^84 + 9*x^83 + 4*x^82 + 111*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 115*x^75 + 84*x^74 + 69*x^73 + 86*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 82*x^68 + 119*x^67 + 12*x^66 + 49*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 105*x^27 + 12*x^26 + 95*x^25 + 18*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 22*x^20 + 109*x^19 + 84*x^18 + 107*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 87*x^11 + 4*x^10 + x^9 + 30*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 42*x^4 + 43*x^3 + 92*x^2 + 93*x + 126, x^95 + 15*x^93 + 94*x^92 + 117*x^91 + 28*x^90 + 51*x^89 + 74*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 126*x^84 + 73*x^83 + 68*x^82 + 47*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 51*x^75 + 20*x^74 + 5*x^73 + 118*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 50*x^68 + 55*x^67 + 76*x^66 + 113*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 41*x^27 + 76*x^26 + 31*x^25 + 114*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 54*x^20 + 45*x^19 + 20*x^18 + 43*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 23*x^11 + 68*x^10 + 65*x^9 + 62*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 10*x^4 + 107*x^3 + 28*x^2 + 29*x + 30, x^95 + 15*x^93 + 74*x^92 + 101*x^91 + 20*x^90 + 35*x^89 + 46*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 42*x^84 + 25*x^83 + 12*x^82 + 127*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 3*x^75 + 124*x^74 + 85*x^73 + 18*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 102*x^68 + 39*x^67 + 36*x^66 + 97*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 89*x^27 + 36*x^26 + 79*x^25 + 102*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 18*x^20 + 61*x^19 + 124*x^18 + 59*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 39*x^11 + 12*x^10 + 81*x^9 + 42*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 46*x^4 + 27*x^3 + 20*x^2 + 77*x + 74, x^95 + 15*x^93 + 70*x^92 + 85*x^91 + 60*x^90 + 115*x^89 + 82*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 70*x^84 + 105*x^83 + 100*x^82 + 111*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 83*x^75 + 116*x^74 + 69*x^73 + 46*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 106*x^68 + 23*x^67 + 44*x^66 + 49*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 9*x^27 + 108*x^26 + 95*x^25 + 26*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 30*x^20 + 77*x^19 + 52*x^18 + 107*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 55*x^11 + 36*x^10 + x^9 + 22*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 98*x^4 + 75*x^3 + 124*x^2 + 93*x + 86, x^95 + 15*x^93 + 6*x^92 + 5*x^91 + 76*x^90 + 67*x^89 + 66*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 38*x^84 + 121*x^83 + 20*x^82 + 95*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 99*x^75 + 36*x^74 + 53*x^73 + 126*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 74*x^68 + 71*x^67 + 60*x^66 + x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 121*x^27 + 60*x^26 + 111*x^25 + 74*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 126*x^20 + 29*x^19 + 36*x^18 + 27*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 7*x^11 + 20*x^10 + 49*x^9 + 38*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 66*x^4 + 59*x^3 + 76*x^2 + 109*x + 6, x^95 + 15*x^93 + 114*x^92 + 69*x^91 + 52*x^90 + 99*x^89 + 54*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 50*x^84 + 57*x^83 + 44*x^82 + 63*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 35*x^75 + 92*x^74 + 21*x^73 + 74*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 94*x^68 + 7*x^67 + 4*x^66 + 33*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 57*x^27 + 68*x^26 + 15*x^25 + 14*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 58*x^20 + 93*x^19 + 28*x^18 + 123*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 71*x^11 + 108*x^10 + 17*x^9 + 2*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 70*x^4 + 123*x^3 + 116*x^2 + 13*x + 2, x^95 + 15*x^93 + 38*x^92 + 117*x^91 + 124*x^90 + 83*x^89 + 114*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 38*x^84 + 73*x^83 + 36*x^82 + 15*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 51*x^75 + 52*x^74 + 101*x^73 + 14*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 10*x^68 + 55*x^67 + 108*x^66 + 17*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 41*x^27 + 44*x^26 + 63*x^25 + 58*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 126*x^20 + 45*x^19 + 116*x^18 + 11*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 23*x^11 + 100*x^10 + 33*x^9 + 118*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 2*x^4 + 107*x^3 + 60*x^2 + 61*x + 54, x^95 + 15*x^93 + 94*x^92 + 85*x^91 + 92*x^90 + 19*x^89 + 74*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 126*x^84 + 105*x^83 + 4*x^82 + 79*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 83*x^75 + 84*x^74 + 37*x^73 + 118*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 50*x^68 + 23*x^67 + 12*x^66 + 81*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 9*x^27 + 12*x^26 + 127*x^25 + 114*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 54*x^20 + 77*x^19 + 84*x^18 + 75*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 55*x^11 + 4*x^10 + 97*x^9 + 62*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 10*x^4 + 75*x^3 + 92*x^2 + 125*x + 30, x^95 + 15*x^93 + 30*x^92 + 101*x^91 + 108*x^90 + 3*x^89 + 58*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 94*x^84 + 25*x^83 + 52*x^82 + 31*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 3*x^75 + 4*x^74 + 117*x^73 + 70*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 18*x^68 + 39*x^67 + 28*x^66 + 65*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 89*x^27 + 92*x^26 + 47*x^25 + 34*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 22*x^20 + 61*x^19 + 68*x^18 + 91*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 39*x^11 + 116*x^10 + 113*x^9 + 78*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 106*x^4 + 27*x^3 + 44*x^2 + 45*x + 78, x^95 + 15*x^93 + 26*x^92 + 117*x^91 + 4*x^90 + 83*x^89 + 78*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 26*x^84 + 73*x^83 + 92*x^82 + 15*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 51*x^75 + 76*x^74 + 101*x^73 + 50*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 54*x^68 + 55*x^67 + 20*x^66 + 17*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 41*x^27 + 84*x^26 + 63*x^25 + 6*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 66*x^20 + 45*x^19 + 12*x^18 + 11*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 23*x^11 + 28*x^10 + 33*x^9 + 74*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 62*x^4 + 107*x^3 + 68*x^2 + 61*x + 10, x^95 + 15*x^93 + 26*x^92 + 37*x^91 + 52*x^90 + 35*x^89 + 94*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 122*x^84 + 89*x^83 + 108*x^82 + 127*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 67*x^75 + 92*x^74 + 85*x^73 + 98*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 22*x^68 + 103*x^67 + 68*x^66 + 97*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 25*x^27 + 68*x^26 + 79*x^25 + 86*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 34*x^20 + 125*x^19 + 92*x^18 + 59*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 103*x^11 + 108*x^10 + 81*x^9 + 58*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 30*x^4 + 91*x^3 + 52*x^2 + 77*x + 90, x^95 + 15*x^93 + 86*x^92 + 85*x^91 + 92*x^90 + 115*x^89 + 2*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 86*x^84 + 105*x^83 + 68*x^82 + 111*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 83*x^75 + 84*x^74 + 69*x^73 + 126*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 90*x^68 + 23*x^67 + 76*x^66 + 49*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 9*x^27 + 12*x^26 + 95*x^25 + 10*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 110*x^20 + 77*x^19 + 20*x^18 + 107*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 55*x^11 + 4*x^10 + x^9 + 38*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 18*x^4 + 75*x^3 + 28*x^2 + 93*x + 102, x^95 + 15*x^93 + 78*x^92 + 5*x^91 + 44*x^90 + 35*x^89 + 42*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 78*x^84 + 121*x^83 + 116*x^82 + 127*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 99*x^75 + 68*x^74 + 85*x^73 + 86*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 34*x^68 + 71*x^67 + 92*x^66 + 97*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 121*x^27 + 28*x^26 + 79*x^25 + 82*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 70*x^20 + 29*x^19 + 4*x^18 + 59*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 7*x^11 + 52*x^10 + 81*x^9 + 30*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 58*x^4 + 59*x^3 + 108*x^2 + 77*x + 94, x^95 + 15*x^93 + 110*x^92 + 5*x^91 + 12*x^90 + 99*x^89 + 42*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 46*x^84 + 121*x^83 + 20*x^82 + 63*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 99*x^75 + 100*x^74 + 21*x^73 + 86*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 66*x^68 + 71*x^67 + 60*x^66 + 33*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 121*x^27 + 124*x^26 + 15*x^25 + 82*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 38*x^20 + 29*x^19 + 36*x^18 + 123*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 7*x^11 + 84*x^10 + 17*x^9 + 30*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 90*x^4 + 59*x^3 + 76*x^2 + 13*x + 30, x^95 + 15*x^93 + 42*x^92 + 53*x^91 + 100*x^90 + 19*x^89 + 62*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 42*x^84 + 9*x^83 + 124*x^82 + 79*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 115*x^75 + 108*x^74 + 37*x^73 + 66*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 38*x^68 + 119*x^67 + 116*x^66 + 81*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 105*x^27 + 52*x^26 + 127*x^25 + 54*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 18*x^20 + 109*x^19 + 44*x^18 + 75*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 87*x^11 + 60*x^10 + 97*x^9 + 26*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 110*x^4 + 43*x^3 + 36*x^2 + 125*x + 90, x^95 + 15*x^93 + 22*x^92 + 21*x^91 + 92*x^90 + 51*x^89 + 66*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 22*x^84 + 41*x^83 + 68*x^82 + 47*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 19*x^75 + 84*x^74 + 5*x^73 + 62*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 26*x^68 + 87*x^67 + 76*x^66 + 113*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 73*x^27 + 12*x^26 + 31*x^25 + 74*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 46*x^20 + 13*x^19 + 20*x^18 + 43*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 119*x^11 + 4*x^10 + 65*x^9 + 102*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 82*x^4 + 11*x^3 + 28*x^2 + 29*x + 38, x^95 + 15*x^93 + 54*x^92 + 85*x^91 + 28*x^90 + 51*x^89 + 98*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 54*x^84 + 105*x^83 + 4*x^82 + 47*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 83*x^75 + 20*x^74 + 5*x^73 + 30*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 122*x^68 + 23*x^67 + 12*x^66 + 113*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 9*x^27 + 76*x^26 + 31*x^25 + 106*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 78*x^20 + 77*x^19 + 84*x^18 + 43*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 55*x^11 + 68*x^10 + 65*x^9 + 70*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 50*x^4 + 75*x^3 + 92*x^2 + 29*x + 6, x^95 + 15*x^93 + 82*x^92 + 21*x^91 + 100*x^90 + 83*x^89 + 102*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 114*x^84 + 41*x^83 + 60*x^82 + 15*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 19*x^75 + 108*x^74 + 101*x^73 + 90*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 94*x^68 + 87*x^67 + 52*x^66 + 17*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 73*x^27 + 52*x^26 + 63*x^25 + 126*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 122*x^20 + 13*x^19 + 108*x^18 + 11*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 119*x^11 + 60*x^10 + 33*x^9 + 82*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 70*x^4 + 11*x^3 + 100*x^2 + 61*x + 50, x^95 + 15*x^93 + 118*x^92 + 69*x^91 + 76*x^90 + 3*x^89 + 114*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 86*x^84 + 57*x^83 + 20*x^82 + 31*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 35*x^75 + 36*x^74 + 117*x^73 + 78*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 26*x^68 + 7*x^67 + 60*x^66 + 65*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 57*x^27 + 60*x^26 + 47*x^25 + 58*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 110*x^20 + 93*x^19 + 36*x^18 + 91*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 71*x^11 + 20*x^10 + 113*x^9 + 54*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 82*x^4 + 123*x^3 + 76*x^2 + 45*x + 86, x^95 + 15*x^93 + 30*x^92 + 85*x^91 + 92*x^90 + 83*x^89 + 74*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 62*x^84 + 105*x^83 + 4*x^82 + 15*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 83*x^75 + 84*x^74 + 101*x^73 + 118*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 114*x^68 + 23*x^67 + 12*x^66 + 17*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 9*x^27 + 12*x^26 + 63*x^25 + 114*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 118*x^20 + 77*x^19 + 84*x^18 + 11*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 55*x^11 + 4*x^10 + 33*x^9 + 62*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 74*x^4 + 75*x^3 + 92*x^2 + 61*x + 30, x^95 + 15*x^93 + 78*x^92 + 21*x^91 + 124*x^90 + 19*x^89 + 26*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 110*x^84 + 41*x^83 + 100*x^82 + 79*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 19*x^75 + 52*x^74 + 37*x^73 + 38*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 66*x^68 + 87*x^67 + 44*x^66 + 81*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 73*x^27 + 44*x^26 + 127*x^25 + 2*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 102*x^20 + 13*x^19 + 52*x^18 + 75*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 119*x^11 + 100*x^10 + 97*x^9 + 46*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 90*x^4 + 11*x^3 + 124*x^2 + 125*x + 14, x^95 + 15*x^93 + 122*x^92 + 21*x^91 + 100*x^90 + 51*x^89 + 78*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 58*x^84 + 41*x^83 + 124*x^82 + 47*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 19*x^75 + 108*x^74 + 5*x^73 + 50*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 22*x^68 + 87*x^67 + 116*x^66 + 113*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 73*x^27 + 52*x^26 + 31*x^25 + 6*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 98*x^20 + 13*x^19 + 44*x^18 + 43*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 119*x^11 + 60*x^10 + 65*x^9 + 74*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 30*x^4 + 11*x^3 + 36*x^2 + 29*x + 74, x^95 + 15*x^93 + 18*x^92 + 85*x^91 + 4*x^90 + 83*x^89 + 70*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 114*x^84 + 105*x^83 + 28*x^82 + 15*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 83*x^75 + 76*x^74 + 101*x^73 + 122*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 94*x^68 + 23*x^67 + 84*x^66 + 17*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 9*x^27 + 84*x^26 + 63*x^25 + 94*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 122*x^20 + 77*x^19 + 76*x^18 + 11*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 55*x^11 + 28*x^10 + 33*x^9 + 114*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 70*x^4 + 75*x^3 + 4*x^2 + 61*x + 18, x^95 + 15*x^93 + 14*x^92 + 117*x^91 + 124*x^90 + 115*x^89 + 26*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 46*x^84 + 73*x^83 + 100*x^82 + 111*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 51*x^75 + 52*x^74 + 69*x^73 + 38*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 2*x^68 + 55*x^67 + 44*x^66 + 49*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 41*x^27 + 44*x^26 + 95*x^25 + 2*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 38*x^20 + 45*x^19 + 52*x^18 + 107*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 23*x^11 + 100*x^10 + x^9 + 46*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 26*x^4 + 107*x^3 + 124*x^2 + 93*x + 14, x^95 + 15*x^93 + 66*x^92 + 21*x^91 + 36*x^90 + 83*x^89 + 86*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 34*x^84 + 41*x^83 + 124*x^82 + 15*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 19*x^75 + 44*x^74 + 101*x^73 + 106*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 46*x^68 + 87*x^67 + 116*x^66 + 17*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 73*x^27 + 116*x^26 + 63*x^25 + 46*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 106*x^20 + 13*x^19 + 44*x^18 + 11*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 119*x^11 + 124*x^10 + 33*x^9 + 34*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 86*x^4 + 11*x^3 + 36*x^2 + 61*x + 66, x^95 + 15*x^93 + 50*x^92 + 5*x^91 + 52*x^90 + 99*x^89 + 54*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 114*x^84 + 121*x^83 + 44*x^82 + 63*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 99*x^75 + 92*x^74 + 21*x^73 + 74*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 30*x^68 + 71*x^67 + 4*x^66 + 33*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 121*x^27 + 68*x^26 + 15*x^25 + 14*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 122*x^20 + 29*x^19 + 28*x^18 + 123*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 7*x^11 + 108*x^10 + 17*x^9 + 2*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 6*x^4 + 59*x^3 + 116*x^2 + 13*x + 2, x^95 + 15*x^93 + 94*x^92 + 85*x^91 + 92*x^90 + 83*x^89 + 10*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 126*x^84 + 105*x^83 + 4*x^82 + 15*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 83*x^75 + 84*x^74 + 101*x^73 + 54*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 50*x^68 + 23*x^67 + 12*x^66 + 17*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 9*x^27 + 12*x^26 + 63*x^25 + 50*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 54*x^20 + 77*x^19 + 84*x^18 + 11*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 55*x^11 + 4*x^10 + 33*x^9 + 126*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 10*x^4 + 75*x^3 + 92*x^2 + 61*x + 94, x^95 + 15*x^93 + 42*x^92 + 101*x^91 + 20*x^90 + 99*x^89 + 78*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 10*x^84 + 25*x^83 + 12*x^82 + 63*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 3*x^75 + 124*x^74 + 21*x^73 + 114*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 6*x^68 + 39*x^67 + 36*x^66 + 33*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 89*x^27 + 36*x^26 + 15*x^25 + 6*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 114*x^20 + 61*x^19 + 124*x^18 + 123*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 39*x^11 + 12*x^10 + 17*x^9 + 10*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 78*x^4 + 27*x^3 + 20*x^2 + 13*x + 42, x^95 + 15*x^93 + 2*x^92 + 85*x^91 + 4*x^90 + 83*x^89 + 118*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 34*x^84 + 105*x^83 + 28*x^82 + 15*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 83*x^75 + 76*x^74 + 101*x^73 + 74*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 46*x^68 + 23*x^67 + 84*x^66 + 17*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 9*x^27 + 84*x^26 + 63*x^25 + 78*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 106*x^20 + 77*x^19 + 76*x^18 + 11*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 55*x^11 + 28*x^10 + 33*x^9 + 2*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 86*x^4 + 75*x^3 + 4*x^2 + 61*x + 98, x^95 + 15*x^93 + 78*x^92 + 117*x^91 + 124*x^90 + 115*x^89 + 90*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 110*x^84 + 73*x^83 + 100*x^82 + 111*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 51*x^75 + 52*x^74 + 69*x^73 + 102*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 66*x^68 + 55*x^67 + 44*x^66 + 49*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 41*x^27 + 44*x^26 + 95*x^25 + 66*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 102*x^20 + 45*x^19 + 52*x^18 + 107*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 23*x^11 + 100*x^10 + x^9 + 110*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 90*x^4 + 107*x^3 + 124*x^2 + 93*x + 78, x^95 + 15*x^93 + 70*x^92 + 85*x^91 + 28*x^90 + 51*x^89 + 50*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 6*x^84 + 105*x^83 + 4*x^82 + 47*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 83*x^75 + 20*x^74 + 5*x^73 + 78*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 42*x^68 + 23*x^67 + 12*x^66 + 113*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 9*x^27 + 76*x^26 + 31*x^25 + 122*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 94*x^20 + 77*x^19 + 84*x^18 + 43*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 55*x^11 + 68*x^10 + 65*x^9 + 54*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 34*x^4 + 75*x^3 + 92*x^2 + 29*x + 54, x^95 + 15*x^93 + 62*x^92 + 69*x^91 + 12*x^90 + 99*x^89 + 122*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 62*x^84 + 57*x^83 + 20*x^82 + 63*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 35*x^75 + 100*x^74 + 21*x^73 + 6*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 50*x^68 + 7*x^67 + 60*x^66 + 33*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 57*x^27 + 124*x^26 + 15*x^25 + 98*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 118*x^20 + 93*x^19 + 36*x^18 + 123*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 71*x^11 + 84*x^10 + 17*x^9 + 14*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 10*x^4 + 123*x^3 + 76*x^2 + 13*x + 78, x^95 + 15*x^93 + 98*x^92 + 85*x^91 + 100*x^90 + 19*x^89 + 54*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 66*x^84 + 105*x^83 + 60*x^82 + 79*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 83*x^75 + 108*x^74 + 37*x^73 + 10*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 14*x^68 + 23*x^67 + 52*x^66 + 81*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 9*x^27 + 52*x^26 + 127*x^25 + 14*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 10*x^20 + 77*x^19 + 108*x^18 + 75*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 55*x^11 + 60*x^10 + 97*x^9 + 66*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 54*x^4 + 75*x^3 + 100*x^2 + 125*x + 98, x^95 + 15*x^93 + 66*x^92 + 85*x^91 + 4*x^90 + 19*x^89 + 118*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 98*x^84 + 105*x^83 + 28*x^82 + 79*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 83*x^75 + 76*x^74 + 37*x^73 + 74*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 110*x^68 + 23*x^67 + 84*x^66 + 81*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 9*x^27 + 84*x^26 + 127*x^25 + 78*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 42*x^20 + 77*x^19 + 76*x^18 + 75*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 55*x^11 + 28*x^10 + 97*x^9 + 2*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 22*x^4 + 75*x^3 + 4*x^2 + 125*x + 98, x^95 + 15*x^93 + 62*x^92 + 37*x^91 + 108*x^90 + 67*x^89 + 90*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 126*x^84 + 89*x^83 + 52*x^82 + 95*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 67*x^75 + 4*x^74 + 53*x^73 + 38*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 114*x^68 + 103*x^67 + 28*x^66 + x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 25*x^27 + 92*x^26 + 111*x^25 + 66*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 54*x^20 + 125*x^19 + 68*x^18 + 27*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 103*x^11 + 116*x^10 + 49*x^9 + 46*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 74*x^4 + 91*x^3 + 44*x^2 + 109*x + 46, x^95 + 15*x^93 + 70*x^92 + 5*x^91 + 108*x^90 + 67*x^89 + 98*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 38*x^84 + 121*x^83 + 116*x^82 + 95*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 99*x^75 + 4*x^74 + 53*x^73 + 94*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 74*x^68 + 71*x^67 + 92*x^66 + x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 121*x^27 + 92*x^26 + 111*x^25 + 106*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 126*x^20 + 29*x^19 + 4*x^18 + 27*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 7*x^11 + 116*x^10 + 49*x^9 + 6*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 66*x^4 + 59*x^3 + 108*x^2 + 109*x + 38, x^95 + 15*x^93 + 118*x^92 + 69*x^91 + 108*x^90 + 3*x^89 + 82*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 22*x^84 + 57*x^83 + 116*x^82 + 31*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 35*x^75 + 4*x^74 + 117*x^73 + 110*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 90*x^68 + 7*x^67 + 92*x^66 + 65*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 57*x^27 + 92*x^26 + 47*x^25 + 26*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 46*x^20 + 93*x^19 + 4*x^18 + 91*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 71*x^11 + 116*x^10 + 113*x^9 + 86*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 18*x^4 + 123*x^3 + 108*x^2 + 45*x + 54, x^95 + 15*x^93 + 62*x^92 + 101*x^91 + 12*x^90 + 67*x^89 + 122*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 62*x^84 + 25*x^83 + 20*x^82 + 95*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 3*x^75 + 100*x^74 + 53*x^73 + 6*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 50*x^68 + 39*x^67 + 60*x^66 + x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 89*x^27 + 124*x^26 + 111*x^25 + 98*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 118*x^20 + 61*x^19 + 36*x^18 + 27*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 39*x^11 + 84*x^10 + 49*x^9 + 14*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 10*x^4 + 27*x^3 + 76*x^2 + 109*x + 78, x^95 + 15*x^93 + 54*x^92 + 21*x^91 + 60*x^90 + 51*x^89 + 2*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 118*x^84 + 41*x^83 + 100*x^82 + 47*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 19*x^75 + 116*x^74 + 5*x^73 + 126*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 58*x^68 + 87*x^67 + 44*x^66 + 113*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 73*x^27 + 108*x^26 + 31*x^25 + 10*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 14*x^20 + 13*x^19 + 52*x^18 + 43*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 119*x^11 + 36*x^10 + 65*x^9 + 38*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 114*x^4 + 11*x^3 + 124*x^2 + 29*x + 38, x^95 + 15*x^93 + 30*x^92 + 53*x^91 + 92*x^90 + 51*x^89 + 10*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 62*x^84 + 9*x^83 + 4*x^82 + 47*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 115*x^75 + 84*x^74 + 5*x^73 + 54*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 114*x^68 + 119*x^67 + 12*x^66 + 113*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 105*x^27 + 12*x^26 + 31*x^25 + 50*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 118*x^20 + 109*x^19 + 84*x^18 + 43*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 87*x^11 + 4*x^10 + 65*x^9 + 126*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 74*x^4 + 43*x^3 + 92*x^2 + 29*x + 94, x^95 + 15*x^93 + 82*x^92 + 69*x^91 + 52*x^90 + 99*x^89 + 22*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 18*x^84 + 57*x^83 + 44*x^82 + 63*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 35*x^75 + 92*x^74 + 21*x^73 + 106*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 126*x^68 + 7*x^67 + 4*x^66 + 33*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 57*x^27 + 68*x^26 + 15*x^25 + 110*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 26*x^20 + 93*x^19 + 28*x^18 + 123*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 71*x^11 + 108*x^10 + 17*x^9 + 34*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 102*x^4 + 123*x^3 + 116*x^2 + 13*x + 34, x^95 + 15*x^93 + 54*x^92 + 37*x^91 + 76*x^90 + 99*x^89 + 114*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 22*x^84 + 89*x^83 + 20*x^82 + 63*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 67*x^75 + 36*x^74 + 21*x^73 + 78*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 90*x^68 + 103*x^67 + 60*x^66 + 33*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 25*x^27 + 60*x^26 + 15*x^25 + 58*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 46*x^20 + 125*x^19 + 36*x^18 + 123*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 103*x^11 + 20*x^10 + 17*x^9 + 54*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 18*x^4 + 91*x^3 + 76*x^2 + 13*x + 86, x^95 + 15*x^93 + 14*x^92 + 69*x^91 + 44*x^90 + 99*x^89 + 106*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 14*x^84 + 57*x^83 + 116*x^82 + 63*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 35*x^75 + 68*x^74 + 21*x^73 + 22*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 98*x^68 + 7*x^67 + 92*x^66 + 33*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 57*x^27 + 28*x^26 + 15*x^25 + 18*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 6*x^20 + 93*x^19 + 4*x^18 + 123*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 71*x^11 + 52*x^10 + 17*x^9 + 94*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 122*x^4 + 123*x^3 + 108*x^2 + 13*x + 30, x^95 + 15*x^93 + 10*x^92 + 5*x^91 + 84*x^90 + 67*x^89 + 110*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 106*x^84 + 121*x^83 + 76*x^82 + 95*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 99*x^75 + 60*x^74 + 53*x^73 + 82*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 38*x^68 + 71*x^67 + 100*x^66 + x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 121*x^27 + 100*x^26 + 111*x^25 + 38*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 82*x^20 + 29*x^19 + 60*x^18 + 27*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 7*x^11 + 76*x^10 + 49*x^9 + 106*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 110*x^4 + 59*x^3 + 84*x^2 + 109*x + 10, x^95 + 15*x^93 + 102*x^92 + 117*x^91 + 60*x^90 + 19*x^89 + 50*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 102*x^84 + 73*x^83 + 100*x^82 + 79*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 51*x^75 + 116*x^74 + 37*x^73 + 78*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 74*x^68 + 55*x^67 + 44*x^66 + 81*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 41*x^27 + 108*x^26 + 127*x^25 + 122*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 62*x^20 + 45*x^19 + 52*x^18 + 75*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 23*x^11 + 36*x^10 + 97*x^9 + 54*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 66*x^4 + 107*x^3 + 124*x^2 + 125*x + 118, x^95 + 15*x^93 + 38*x^92 + 5*x^91 + 12*x^90 + 3*x^89 + 98*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 70*x^84 + 121*x^83 + 84*x^82 + 31*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 99*x^75 + 100*x^74 + 117*x^73 + 94*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 42*x^68 + 71*x^67 + 124*x^66 + 65*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 121*x^27 + 124*x^26 + 47*x^25 + 106*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 30*x^20 + 29*x^19 + 100*x^18 + 91*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 7*x^11 + 84*x^10 + 113*x^9 + 6*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 34*x^4 + 59*x^3 + 12*x^2 + 45*x + 102, x^95 + 15*x^93 + 14*x^92 + 69*x^91 + 108*x^90 + 35*x^89 + 106*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 14*x^84 + 57*x^83 + 52*x^82 + 127*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 35*x^75 + 4*x^74 + 85*x^73 + 22*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 98*x^68 + 7*x^67 + 28*x^66 + 97*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 57*x^27 + 92*x^26 + 79*x^25 + 18*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 6*x^20 + 93*x^19 + 68*x^18 + 59*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 71*x^11 + 116*x^10 + 81*x^9 + 94*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 122*x^4 + 123*x^3 + 44*x^2 + 77*x + 30, x^95 + 15*x^93 + 70*x^92 + 69*x^91 + 76*x^90 + 3*x^89 + 2*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 102*x^84 + 57*x^83 + 20*x^82 + 31*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 35*x^75 + 36*x^74 + 117*x^73 + 62*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 10*x^68 + 7*x^67 + 60*x^66 + 65*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 57*x^27 + 60*x^26 + 47*x^25 + 10*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 62*x^20 + 93*x^19 + 36*x^18 + 91*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 71*x^11 + 20*x^10 + 113*x^9 + 102*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 2*x^4 + 123*x^3 + 76*x^2 + 45*x + 70, x^95 + 15*x^93 + 54*x^92 + 69*x^91 + 76*x^90 + 3*x^89 + 50*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 22*x^84 + 57*x^83 + 20*x^82 + 31*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 35*x^75 + 36*x^74 + 117*x^73 + 14*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 90*x^68 + 7*x^67 + 60*x^66 + 65*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 57*x^27 + 60*x^26 + 47*x^25 + 122*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 46*x^20 + 93*x^19 + 36*x^18 + 91*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 71*x^11 + 20*x^10 + 113*x^9 + 118*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 18*x^4 + 123*x^3 + 76*x^2 + 45*x + 22, x^95 + 15*x^93 + 26*x^92 + 21*x^91 + 68*x^90 + 115*x^89 + 78*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 26*x^84 + 41*x^83 + 28*x^82 + 111*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 19*x^75 + 12*x^74 + 69*x^73 + 50*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 54*x^68 + 87*x^67 + 84*x^66 + 49*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 73*x^27 + 20*x^26 + 95*x^25 + 6*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 66*x^20 + 13*x^19 + 76*x^18 + 107*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 119*x^11 + 92*x^10 + x^9 + 74*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 62*x^4 + 11*x^3 + 4*x^2 + 93*x + 10, x^95 + 15*x^93 + 2*x^92 + 21*x^91 + 4*x^90 + 19*x^89 + 118*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 34*x^84 + 41*x^83 + 28*x^82 + 79*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 19*x^75 + 76*x^74 + 37*x^73 + 74*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 46*x^68 + 87*x^67 + 84*x^66 + 81*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 73*x^27 + 84*x^26 + 127*x^25 + 78*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 106*x^20 + 13*x^19 + 76*x^18 + 75*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 119*x^11 + 28*x^10 + 97*x^9 + 2*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 86*x^4 + 11*x^3 + 4*x^2 + 125*x + 98, x^95 + 15*x^93 + 70*x^92 + 101*x^91 + 108*x^90 + 35*x^89 + 34*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 38*x^84 + 25*x^83 + 116*x^82 + 127*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 3*x^75 + 4*x^74 + 85*x^73 + 30*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 74*x^68 + 39*x^67 + 92*x^66 + 97*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 89*x^27 + 92*x^26 + 79*x^25 + 42*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 126*x^20 + 61*x^19 + 4*x^18 + 59*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 39*x^11 + 116*x^10 + 81*x^9 + 70*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 66*x^4 + 27*x^3 + 108*x^2 + 77*x + 102, x^95 + 15*x^93 + 98*x^92 + 69*x^91 + 84*x^90 + 99*x^89 + 70*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 34*x^84 + 57*x^83 + 12*x^82 + 63*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 35*x^75 + 60*x^74 + 21*x^73 + 58*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 110*x^68 + 7*x^67 + 36*x^66 + 33*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 57*x^27 + 100*x^26 + 15*x^25 + 94*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 106*x^20 + 93*x^19 + 124*x^18 + 123*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 71*x^11 + 76*x^10 + 17*x^9 + 50*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 22*x^4 + 123*x^3 + 20*x^2 + 13*x + 50, x^95 + 15*x^93 + 26*x^92 + 21*x^91 + 100*x^90 + 51*x^89 + 110*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 90*x^84 + 41*x^83 + 124*x^82 + 47*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 19*x^75 + 108*x^74 + 5*x^73 + 18*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 118*x^68 + 87*x^67 + 116*x^66 + 113*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 73*x^27 + 52*x^26 + 31*x^25 + 38*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 2*x^20 + 13*x^19 + 44*x^18 + 43*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 119*x^11 + 60*x^10 + 65*x^9 + 42*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 126*x^4 + 11*x^3 + 36*x^2 + 29*x + 42, x^95 + 15*x^93 + 70*x^92 + 21*x^91 + 124*x^90 + 115*x^89 + 82*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 70*x^84 + 41*x^83 + 36*x^82 + 111*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 19*x^75 + 52*x^74 + 69*x^73 + 46*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 106*x^68 + 87*x^67 + 108*x^66 + 49*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 73*x^27 + 44*x^26 + 95*x^25 + 26*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 30*x^20 + 13*x^19 + 116*x^18 + 107*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 119*x^11 + 100*x^10 + x^9 + 22*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 98*x^4 + 11*x^3 + 60*x^2 + 93*x + 86, x^95 + 15*x^93 + 22*x^92 + 85*x^91 + 28*x^90 + 115*x^89 + 2*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 22*x^84 + 105*x^83 + 4*x^82 + 111*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 83*x^75 + 20*x^74 + 69*x^73 + 126*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 26*x^68 + 23*x^67 + 12*x^66 + 49*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 9*x^27 + 76*x^26 + 95*x^25 + 10*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 46*x^20 + 77*x^19 + 84*x^18 + 107*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 55*x^11 + 68*x^10 + x^9 + 38*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 82*x^4 + 75*x^3 + 92*x^2 + 93*x + 102, x^95 + 15*x^93 + 34*x^92 + 21*x^91 + 68*x^90 + 19*x^89 + 86*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 66*x^84 + 41*x^83 + 92*x^82 + 79*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 19*x^75 + 12*x^74 + 37*x^73 + 106*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 14*x^68 + 87*x^67 + 20*x^66 + 81*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 73*x^27 + 20*x^26 + 127*x^25 + 46*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 10*x^20 + 13*x^19 + 12*x^18 + 75*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 119*x^11 + 92*x^10 + 97*x^9 + 34*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 54*x^4 + 11*x^3 + 68*x^2 + 125*x + 2, x^95 + 15*x^93 + 46*x^92 + 69*x^91 + 108*x^90 + 35*x^89 + 10*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 46*x^84 + 57*x^83 + 52*x^82 + 127*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 35*x^75 + 4*x^74 + 85*x^73 + 118*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 66*x^68 + 7*x^67 + 28*x^66 + 97*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 57*x^27 + 92*x^26 + 79*x^25 + 50*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 38*x^20 + 93*x^19 + 68*x^18 + 59*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 71*x^11 + 116*x^10 + 81*x^9 + 62*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 90*x^4 + 123*x^3 + 44*x^2 + 77*x + 126, x^95 + 15*x^93 + 18*x^92 + 53*x^91 + 100*x^90 + 115*x^89 + 102*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 50*x^84 + 9*x^83 + 60*x^82 + 111*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 115*x^75 + 108*x^74 + 69*x^73 + 90*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 30*x^68 + 119*x^67 + 52*x^66 + 49*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 105*x^27 + 52*x^26 + 95*x^25 + 126*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 58*x^20 + 109*x^19 + 108*x^18 + 107*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 87*x^11 + 60*x^10 + x^9 + 82*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 6*x^4 + 43*x^3 + 100*x^2 + 93*x + 50, x^95 + 15*x^93 + 10*x^92 + 37*x^91 + 52*x^90 + 99*x^89 + 78*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 42*x^84 + 89*x^83 + 108*x^82 + 63*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 67*x^75 + 92*x^74 + 21*x^73 + 114*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 102*x^68 + 103*x^67 + 68*x^66 + 33*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 25*x^27 + 68*x^26 + 15*x^25 + 6*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 18*x^20 + 125*x^19 + 92*x^18 + 123*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 103*x^11 + 108*x^10 + 17*x^9 + 10*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 46*x^4 + 91*x^3 + 52*x^2 + 13*x + 106, x^95 + 15*x^93 + 42*x^92 + 37*x^91 + 52*x^90 + 99*x^89 + 110*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 74*x^84 + 89*x^83 + 108*x^82 + 63*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 67*x^75 + 92*x^74 + 21*x^73 + 82*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 70*x^68 + 103*x^67 + 68*x^66 + 33*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 25*x^27 + 68*x^26 + 15*x^25 + 38*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 50*x^20 + 125*x^19 + 92*x^18 + 123*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 103*x^11 + 108*x^10 + 17*x^9 + 106*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 14*x^4 + 91*x^3 + 52*x^2 + 13*x + 74, x^95 + 15*x^93 + 38*x^92 + 69*x^91 + 12*x^90 + 67*x^89 + 98*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 70*x^84 + 57*x^83 + 84*x^82 + 95*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 35*x^75 + 100*x^74 + 53*x^73 + 94*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 42*x^68 + 7*x^67 + 124*x^66 + x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 57*x^27 + 124*x^26 + 111*x^25 + 106*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 30*x^20 + 93*x^19 + 100*x^18 + 27*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 71*x^11 + 84*x^10 + 49*x^9 + 6*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 34*x^4 + 123*x^3 + 12*x^2 + 109*x + 102, x^95 + 15*x^93 + 18*x^92 + 85*x^91 + 4*x^90 + 19*x^89 + 6*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 114*x^84 + 105*x^83 + 28*x^82 + 79*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 83*x^75 + 76*x^74 + 37*x^73 + 58*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 94*x^68 + 23*x^67 + 84*x^66 + 81*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 9*x^27 + 84*x^26 + 127*x^25 + 30*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 122*x^20 + 77*x^19 + 76*x^18 + 75*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 55*x^11 + 28*x^10 + 97*x^9 + 50*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 70*x^4 + 75*x^3 + 4*x^2 + 125*x + 82, x^95 + 15*x^93 + 38*x^92 + 117*x^91 + 92*x^90 + 19*x^89 + 82*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 102*x^84 + 73*x^83 + 68*x^82 + 79*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 51*x^75 + 84*x^74 + 37*x^73 + 46*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 74*x^68 + 55*x^67 + 76*x^66 + 81*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 41*x^27 + 12*x^26 + 127*x^25 + 26*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 62*x^20 + 45*x^19 + 20*x^18 + 75*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 23*x^11 + 4*x^10 + 97*x^9 + 22*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 66*x^4 + 107*x^3 + 28*x^2 + 125*x + 22, x^95 + 15*x^93 + 110*x^92 + 117*x^91 + 124*x^90 + 115*x^89 + 122*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 14*x^84 + 73*x^83 + 100*x^82 + 111*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 51*x^75 + 52*x^74 + 69*x^73 + 70*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 34*x^68 + 55*x^67 + 44*x^66 + 49*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 41*x^27 + 44*x^26 + 95*x^25 + 98*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 6*x^20 + 45*x^19 + 52*x^18 + 107*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 23*x^11 + 100*x^10 + x^9 + 78*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 58*x^4 + 107*x^3 + 124*x^2 + 93*x + 46, x^95 + 15*x^93 + 30*x^92 + 117*x^91 + 92*x^90 + 51*x^89 + 74*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 62*x^84 + 73*x^83 + 4*x^82 + 47*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 51*x^75 + 84*x^74 + 5*x^73 + 118*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 114*x^68 + 55*x^67 + 12*x^66 + 113*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 41*x^27 + 12*x^26 + 31*x^25 + 114*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 118*x^20 + 45*x^19 + 84*x^18 + 43*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 23*x^11 + 4*x^10 + 65*x^9 + 62*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 74*x^4 + 107*x^3 + 92*x^2 + 29*x + 30, x^95 + 15*x^93 + 50*x^92 + 21*x^91 + 4*x^90 + 83*x^89 + 38*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 18*x^84 + 41*x^83 + 28*x^82 + 15*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 19*x^75 + 76*x^74 + 101*x^73 + 26*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 62*x^68 + 87*x^67 + 84*x^66 + 17*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 73*x^27 + 84*x^26 + 63*x^25 + 62*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 26*x^20 + 13*x^19 + 76*x^18 + 11*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 119*x^11 + 28*x^10 + 33*x^9 + 18*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 38*x^4 + 11*x^3 + 4*x^2 + 61*x + 50, x^95 + 15*x^93 + 78*x^92 + 53*x^91 + 60*x^90 + 51*x^89 + 26*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 110*x^84 + 9*x^83 + 36*x^82 + 47*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 115*x^75 + 116*x^74 + 5*x^73 + 38*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 66*x^68 + 119*x^67 + 108*x^66 + 113*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 105*x^27 + 108*x^26 + 31*x^25 + 2*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 102*x^20 + 109*x^19 + 116*x^18 + 43*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 87*x^11 + 36*x^10 + 65*x^9 + 46*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 90*x^4 + 43*x^3 + 60*x^2 + 29*x + 14, x^95 + 15*x^93 + 98*x^92 + 101*x^91 + 20*x^90 + 67*x^89 + 6*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 34*x^84 + 25*x^83 + 76*x^82 + 95*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 3*x^75 + 124*x^74 + 53*x^73 + 122*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 110*x^68 + 39*x^67 + 100*x^66 + x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 89*x^27 + 36*x^26 + 111*x^25 + 30*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 106*x^20 + 61*x^19 + 60*x^18 + 27*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 39*x^11 + 12*x^10 + 49*x^9 + 114*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 22*x^4 + 27*x^3 + 84*x^2 + 109*x + 114, x^95 + 15*x^93 + 102*x^92 + 85*x^91 + 124*x^90 + 115*x^89 + 50*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 102*x^84 + 105*x^83 + 36*x^82 + 111*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 83*x^75 + 52*x^74 + 69*x^73 + 78*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 74*x^68 + 23*x^67 + 108*x^66 + 49*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 9*x^27 + 44*x^26 + 95*x^25 + 122*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 62*x^20 + 77*x^19 + 116*x^18 + 107*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 55*x^11 + 100*x^10 + x^9 + 54*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 66*x^4 + 75*x^3 + 60*x^2 + 93*x + 118, x^95 + 15*x^93 + 10*x^92 + 21*x^91 + 68*x^90 + 51*x^89 + 62*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 74*x^84 + 41*x^83 + 28*x^82 + 47*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 19*x^75 + 12*x^74 + 5*x^73 + 66*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 6*x^68 + 87*x^67 + 84*x^66 + 113*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 73*x^27 + 20*x^26 + 31*x^25 + 54*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 50*x^20 + 13*x^19 + 76*x^18 + 43*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 119*x^11 + 92*x^10 + 65*x^9 + 26*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 78*x^4 + 11*x^3 + 4*x^2 + 29*x + 26, x^95 + 15*x^93 + 106*x^92 + 117*x^91 + 36*x^90 + 19*x^89 + 126*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 106*x^84 + 73*x^83 + 60*x^82 + 79*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 51*x^75 + 44*x^74 + 37*x^73 + 2*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 102*x^68 + 55*x^67 + 52*x^66 + 81*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 41*x^27 + 116*x^26 + 127*x^25 + 118*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 82*x^20 + 45*x^19 + 108*x^18 + 75*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 23*x^11 + 124*x^10 + 97*x^9 + 90*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 46*x^4 + 107*x^3 + 100*x^2 + 125*x + 26, x^95 + 15*x^93 + 118*x^92 + 53*x^91 + 124*x^90 + 83*x^89 + 66*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 54*x^84 + 9*x^83 + 36*x^82 + 15*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 115*x^75 + 52*x^74 + 101*x^73 + 62*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 122*x^68 + 119*x^67 + 108*x^66 + 17*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 105*x^27 + 44*x^26 + 63*x^25 + 74*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 78*x^20 + 109*x^19 + 116*x^18 + 11*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 87*x^11 + 100*x^10 + 33*x^9 + 102*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 50*x^4 + 43*x^3 + 60*x^2 + 61*x + 102, x^95 + 15*x^93 + 86*x^92 + 53*x^91 + 124*x^90 + 19*x^89 + 98*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 22*x^84 + 9*x^83 + 36*x^82 + 79*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 115*x^75 + 52*x^74 + 37*x^73 + 30*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 26*x^68 + 119*x^67 + 108*x^66 + 81*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 105*x^27 + 44*x^26 + 127*x^25 + 106*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 46*x^20 + 109*x^19 + 116*x^18 + 75*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 87*x^11 + 100*x^10 + 97*x^9 + 70*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 82*x^4 + 43*x^3 + 60*x^2 + 125*x + 70, x^95 + 15*x^93 + 94*x^92 + 53*x^91 + 28*x^90 + 115*x^89 + 74*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 126*x^84 + 9*x^83 + 68*x^82 + 111*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 115*x^75 + 20*x^74 + 69*x^73 + 118*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 50*x^68 + 119*x^67 + 76*x^66 + 49*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 105*x^27 + 76*x^26 + 95*x^25 + 114*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 54*x^20 + 109*x^19 + 20*x^18 + 107*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 87*x^11 + 68*x^10 + x^9 + 62*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 10*x^4 + 43*x^3 + 28*x^2 + 93*x + 30, x^95 + 15*x^93 + 34*x^92 + 37*x^91 + 52*x^90 + 3*x^89 + 38*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 34*x^84 + 89*x^83 + 44*x^82 + 31*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 67*x^75 + 92*x^74 + 117*x^73 + 90*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 110*x^68 + 103*x^67 + 4*x^66 + 65*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 25*x^27 + 68*x^26 + 47*x^25 + 62*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 106*x^20 + 125*x^19 + 28*x^18 + 91*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 103*x^11 + 108*x^10 + 113*x^9 + 82*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 22*x^4 + 91*x^3 + 116*x^2 + 45*x + 18, x^95 + 15*x^93 + 66*x^92 + 69*x^91 + 52*x^90 + 99*x^89 + 70*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 66*x^84 + 57*x^83 + 44*x^82 + 63*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 35*x^75 + 92*x^74 + 21*x^73 + 58*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 78*x^68 + 7*x^67 + 4*x^66 + 33*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 57*x^27 + 68*x^26 + 15*x^25 + 94*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 10*x^20 + 93*x^19 + 28*x^18 + 123*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 71*x^11 + 108*x^10 + 17*x^9 + 50*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 118*x^4 + 123*x^3 + 116*x^2 + 13*x + 114, x^95 + 15*x^93 + 118*x^92 + 21*x^91 + 92*x^90 + 51*x^89 + 34*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 118*x^84 + 41*x^83 + 68*x^82 + 47*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 19*x^75 + 84*x^74 + 5*x^73 + 94*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 58*x^68 + 87*x^67 + 76*x^66 + 113*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 73*x^27 + 12*x^26 + 31*x^25 + 42*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 14*x^20 + 13*x^19 + 20*x^18 + 43*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 119*x^11 + 4*x^10 + 65*x^9 + 6*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 114*x^4 + 11*x^3 + 28*x^2 + 29*x + 70, x^95 + 15*x^93 + 110*x^92 + 53*x^91 + 124*x^90 + 115*x^89 + 58*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 14*x^84 + 9*x^83 + 100*x^82 + 111*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 115*x^75 + 52*x^74 + 69*x^73 + 6*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 34*x^68 + 119*x^67 + 44*x^66 + 49*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 105*x^27 + 44*x^26 + 95*x^25 + 34*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 6*x^20 + 109*x^19 + 52*x^18 + 107*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 87*x^11 + 100*x^10 + x^9 + 14*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 58*x^4 + 43*x^3 + 124*x^2 + 93*x + 110, x^95 + 15*x^93 + 66*x^92 + 53*x^91 + 100*x^90 + 51*x^89 + 22*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 34*x^84 + 9*x^83 + 60*x^82 + 47*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 115*x^75 + 108*x^74 + 5*x^73 + 42*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 46*x^68 + 119*x^67 + 52*x^66 + 113*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 105*x^27 + 52*x^26 + 31*x^25 + 110*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 106*x^20 + 109*x^19 + 108*x^18 + 43*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 87*x^11 + 60*x^10 + 65*x^9 + 98*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 86*x^4 + 43*x^3 + 100*x^2 + 29*x + 2, x^95 + 15*x^93 + 114*x^92 + 85*x^91 + 36*x^90 + 19*x^89 + 70*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 18*x^84 + 105*x^83 + 124*x^82 + 79*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 83*x^75 + 44*x^74 + 37*x^73 + 122*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 62*x^68 + 23*x^67 + 116*x^66 + 81*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 9*x^27 + 116*x^26 + 127*x^25 + 94*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 26*x^20 + 77*x^19 + 44*x^18 + 75*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 55*x^11 + 124*x^10 + 97*x^9 + 114*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 38*x^4 + 75*x^3 + 36*x^2 + 125*x + 82, x^95 + 15*x^93 + 58*x^92 + 37*x^91 + 84*x^90 + 99*x^89 + 30*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 90*x^84 + 89*x^83 + 76*x^82 + 63*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 67*x^75 + 60*x^74 + 21*x^73 + 34*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 54*x^68 + 103*x^67 + 100*x^66 + 33*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 25*x^27 + 100*x^26 + 15*x^25 + 22*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 2*x^20 + 125*x^19 + 60*x^18 + 123*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 103*x^11 + 76*x^10 + 17*x^9 + 122*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 62*x^4 + 91*x^3 + 84*x^2 + 13*x + 90, x^95 + 15*x^93 + 78*x^92 + 101*x^91 + 44*x^90 + 3*x^89 + 106*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 78*x^84 + 25*x^83 + 116*x^82 + 31*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 3*x^75 + 68*x^74 + 117*x^73 + 22*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 34*x^68 + 39*x^67 + 92*x^66 + 65*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 89*x^27 + 28*x^26 + 47*x^25 + 18*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 70*x^20 + 61*x^19 + 4*x^18 + 91*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 39*x^11 + 52*x^10 + 113*x^9 + 94*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 58*x^4 + 27*x^3 + 108*x^2 + 45*x + 30, x^95 + 15*x^93 + 66*x^92 + 101*x^91 + 84*x^90 + 3*x^89 + 102*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 2*x^84 + 25*x^83 + 12*x^82 + 31*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 3*x^75 + 60*x^74 + 117*x^73 + 26*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 14*x^68 + 39*x^67 + 36*x^66 + 65*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 89*x^27 + 100*x^26 + 47*x^25 + 126*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 74*x^20 + 61*x^19 + 124*x^18 + 91*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 39*x^11 + 76*x^10 + 113*x^9 + 18*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 54*x^4 + 27*x^3 + 20*x^2 + 45*x + 18, x^95 + 15*x^93 + 74*x^92 + 53*x^91 + 68*x^90 + 83*x^89 + 62*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 10*x^84 + 9*x^83 + 28*x^82 + 15*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 115*x^75 + 12*x^74 + 101*x^73 + 66*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 70*x^68 + 119*x^67 + 84*x^66 + 17*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 105*x^27 + 20*x^26 + 63*x^25 + 54*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 114*x^20 + 109*x^19 + 76*x^18 + 11*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 87*x^11 + 92*x^10 + 33*x^9 + 26*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 14*x^4 + 43*x^3 + 4*x^2 + 61*x + 26, x^95 + 15*x^93 + 34*x^92 + 85*x^91 + 36*x^90 + 19*x^89 + 54*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 2*x^84 + 105*x^83 + 124*x^82 + 79*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 83*x^75 + 44*x^74 + 37*x^73 + 10*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 78*x^68 + 23*x^67 + 116*x^66 + 81*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 9*x^27 + 116*x^26 + 127*x^25 + 14*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 74*x^20 + 77*x^19 + 44*x^18 + 75*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 55*x^11 + 124*x^10 + 97*x^9 + 66*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 118*x^4 + 75*x^3 + 36*x^2 + 125*x + 98, x^95 + 15*x^93 + 98*x^92 + 101*x^91 + 52*x^90 + 3*x^89 + 38*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 98*x^84 + 25*x^83 + 44*x^82 + 31*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 3*x^75 + 92*x^74 + 117*x^73 + 90*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 46*x^68 + 39*x^67 + 4*x^66 + 65*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 89*x^27 + 68*x^26 + 47*x^25 + 62*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 42*x^20 + 61*x^19 + 28*x^18 + 91*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 39*x^11 + 108*x^10 + 113*x^9 + 82*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 86*x^4 + 27*x^3 + 116*x^2 + 45*x + 18, x^95 + 15*x^93 + 106*x^92 + 69*x^91 + 116*x^90 + 3*x^89 + 46*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 10*x^84 + 57*x^83 + 44*x^82 + 31*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 35*x^75 + 28*x^74 + 117*x^73 + 18*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 6*x^68 + 7*x^67 + 4*x^66 + 65*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 57*x^27 + 4*x^26 + 47*x^25 + 102*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 114*x^20 + 93*x^19 + 28*x^18 + 91*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 71*x^11 + 44*x^10 + 113*x^9 + 42*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 78*x^4 + 123*x^3 + 116*x^2 + 45*x + 10, x^95 + 15*x^93 + 30*x^92 + 85*x^91 + 60*x^90 + 19*x^89 + 42*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 126*x^84 + 105*x^83 + 36*x^82 + 79*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 83*x^75 + 116*x^74 + 37*x^73 + 22*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 50*x^68 + 23*x^67 + 108*x^66 + 81*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 9*x^27 + 108*x^26 + 127*x^25 + 82*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 54*x^20 + 77*x^19 + 116*x^18 + 75*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 55*x^11 + 36*x^10 + 97*x^9 + 94*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 10*x^4 + 75*x^3 + 60*x^2 + 125*x + 126, x^95 + 15*x^93 + 66*x^92 + 117*x^91 + 4*x^90 + 51*x^89 + 54*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 98*x^84 + 73*x^83 + 28*x^82 + 47*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 51*x^75 + 76*x^74 + 5*x^73 + 10*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 110*x^68 + 55*x^67 + 84*x^66 + 113*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 41*x^27 + 84*x^26 + 31*x^25 + 14*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 42*x^20 + 45*x^19 + 76*x^18 + 43*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 23*x^11 + 28*x^10 + 65*x^9 + 66*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 22*x^4 + 107*x^3 + 4*x^2 + 29*x + 34, x^95 + 15*x^93 + 98*x^92 + 21*x^91 + 4*x^90 + 19*x^89 + 86*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 2*x^84 + 41*x^83 + 28*x^82 + 79*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 19*x^75 + 76*x^74 + 37*x^73 + 106*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 78*x^68 + 87*x^67 + 84*x^66 + 81*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 73*x^27 + 84*x^26 + 127*x^25 + 46*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 74*x^20 + 13*x^19 + 76*x^18 + 75*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 119*x^11 + 28*x^10 + 97*x^9 + 34*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 118*x^4 + 11*x^3 + 4*x^2 + 125*x + 2, x^95 + 15*x^93 + 98*x^92 + 53*x^91 + 4*x^90 + 51*x^89 + 22*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 2*x^84 + 9*x^83 + 28*x^82 + 47*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 115*x^75 + 76*x^74 + 5*x^73 + 42*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 78*x^68 + 119*x^67 + 84*x^66 + 113*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 105*x^27 + 84*x^26 + 31*x^25 + 110*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 74*x^20 + 109*x^19 + 76*x^18 + 43*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 87*x^11 + 28*x^10 + 65*x^9 + 98*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 118*x^4 + 43*x^3 + 4*x^2 + 29*x + 66, x^95 + 15*x^93 + 22*x^92 + 69*x^91 + 44*x^90 + 3*x^89 + 50*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 54*x^84 + 57*x^83 + 52*x^82 + 31*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 35*x^75 + 68*x^74 + 117*x^73 + 14*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 58*x^68 + 7*x^67 + 28*x^66 + 65*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 57*x^27 + 28*x^26 + 47*x^25 + 122*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 78*x^20 + 93*x^19 + 68*x^18 + 91*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 71*x^11 + 52*x^10 + 113*x^9 + 118*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 114*x^4 + 123*x^3 + 44*x^2 + 45*x + 86, x^95 + 15*x^93 + 46*x^92 + 37*x^91 + 12*x^90 + 67*x^89 + 106*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 110*x^84 + 89*x^83 + 20*x^82 + 95*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 67*x^75 + 100*x^74 + 53*x^73 + 22*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 2*x^68 + 103*x^67 + 60*x^66 + x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 25*x^27 + 124*x^26 + 111*x^25 + 18*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 102*x^20 + 125*x^19 + 36*x^18 + 27*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 103*x^11 + 84*x^10 + 49*x^9 + 94*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 26*x^4 + 91*x^3 + 76*x^2 + 109*x + 94, x^95 + 15*x^93 + 78*x^92 + 5*x^91 + 76*x^90 + 35*x^89 + 10*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 14*x^84 + 121*x^83 + 84*x^82 + 127*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 99*x^75 + 36*x^74 + 85*x^73 + 118*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 98*x^68 + 71*x^67 + 124*x^66 + 97*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 121*x^27 + 60*x^26 + 79*x^25 + 50*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 6*x^20 + 29*x^19 + 100*x^18 + 59*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 7*x^11 + 20*x^10 + 81*x^9 + 62*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 122*x^4 + 59*x^3 + 12*x^2 + 77*x + 62, x^95 + 15*x^93 + 22*x^92 + 85*x^91 + 124*x^90 + 115*x^89 + 34*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 86*x^84 + 105*x^83 + 36*x^82 + 111*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 83*x^75 + 52*x^74 + 69*x^73 + 94*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 90*x^68 + 23*x^67 + 108*x^66 + 49*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 9*x^27 + 44*x^26 + 95*x^25 + 42*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 110*x^20 + 77*x^19 + 116*x^18 + 107*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 55*x^11 + 100*x^10 + x^9 + 6*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 18*x^4 + 75*x^3 + 60*x^2 + 93*x + 6, x^95 + 15*x^93 + 42*x^92 + 69*x^91 + 20*x^90 + 3*x^89 + 78*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 10*x^84 + 57*x^83 + 12*x^82 + 31*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 35*x^75 + 124*x^74 + 117*x^73 + 114*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 6*x^68 + 7*x^67 + 36*x^66 + 65*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 57*x^27 + 36*x^26 + 47*x^25 + 6*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 114*x^20 + 93*x^19 + 124*x^18 + 91*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 71*x^11 + 12*x^10 + 113*x^9 + 10*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 78*x^4 + 123*x^3 + 20*x^2 + 45*x + 42, x^95 + 15*x^93 + 62*x^92 + 53*x^91 + 60*x^90 + 51*x^89 + 74*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 30*x^84 + 9*x^83 + 36*x^82 + 47*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 115*x^75 + 116*x^74 + 5*x^73 + 118*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 18*x^68 + 119*x^67 + 108*x^66 + 113*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 105*x^27 + 108*x^26 + 31*x^25 + 114*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 86*x^20 + 109*x^19 + 116*x^18 + 43*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 87*x^11 + 36*x^10 + 65*x^9 + 62*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 106*x^4 + 43*x^3 + 60*x^2 + 29*x + 94, x^95 + 15*x^93 + 110*x^92 + 85*x^91 + 92*x^90 + 83*x^89 + 90*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 78*x^84 + 105*x^83 + 4*x^82 + 15*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 83*x^75 + 84*x^74 + 101*x^73 + 102*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 98*x^68 + 23*x^67 + 12*x^66 + 17*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 9*x^27 + 12*x^26 + 63*x^25 + 66*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 70*x^20 + 77*x^19 + 84*x^18 + 11*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 55*x^11 + 4*x^10 + 33*x^9 + 110*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 122*x^4 + 75*x^3 + 92*x^2 + 61*x + 14, x^95 + 15*x^93 + 30*x^92 + 37*x^91 + 76*x^90 + 3*x^89 + 26*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 30*x^84 + 89*x^83 + 84*x^82 + 31*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 67*x^75 + 36*x^74 + 117*x^73 + 102*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 82*x^68 + 103*x^67 + 124*x^66 + 65*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 25*x^27 + 60*x^26 + 47*x^25 + 2*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 86*x^20 + 125*x^19 + 100*x^18 + 91*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 103*x^11 + 20*x^10 + 113*x^9 + 110*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 42*x^4 + 91*x^3 + 12*x^2 + 45*x + 46, x^95 + 15*x^93 + 42*x^92 + 21*x^91 + 100*x^90 + 51*x^89 + 62*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 42*x^84 + 41*x^83 + 124*x^82 + 47*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 19*x^75 + 108*x^74 + 5*x^73 + 66*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 38*x^68 + 87*x^67 + 116*x^66 + 113*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 73*x^27 + 52*x^26 + 31*x^25 + 54*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 18*x^20 + 13*x^19 + 44*x^18 + 43*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 119*x^11 + 60*x^10 + 65*x^9 + 26*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 110*x^4 + 11*x^3 + 36*x^2 + 29*x + 90, x^95 + 15*x^93 + 86*x^92 + 85*x^91 + 28*x^90 + 115*x^89 + 66*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 86*x^84 + 105*x^83 + 4*x^82 + 111*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 83*x^75 + 20*x^74 + 69*x^73 + 62*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 90*x^68 + 23*x^67 + 12*x^66 + 49*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 9*x^27 + 76*x^26 + 95*x^25 + 74*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 110*x^20 + 77*x^19 + 84*x^18 + 107*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 55*x^11 + 68*x^10 + x^9 + 102*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 18*x^4 + 75*x^3 + 92*x^2 + 93*x + 38, x^95 + 15*x^93 + 26*x^92 + 69*x^91 + 20*x^90 + 3*x^89 + 126*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 58*x^84 + 57*x^83 + 12*x^82 + 31*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 35*x^75 + 124*x^74 + 117*x^73 + 66*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 86*x^68 + 7*x^67 + 36*x^66 + 65*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 57*x^27 + 36*x^26 + 47*x^25 + 118*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 98*x^20 + 93*x^19 + 124*x^18 + 91*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 71*x^11 + 12*x^10 + 113*x^9 + 26*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 94*x^4 + 123*x^3 + 20*x^2 + 45*x + 122, x^95 + 15*x^93 + 46*x^92 + 21*x^91 + 28*x^90 + 83*x^89 + 26*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 14*x^84 + 41*x^83 + 68*x^82 + 15*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 19*x^75 + 20*x^74 + 101*x^73 + 38*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 34*x^68 + 87*x^67 + 76*x^66 + 17*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 73*x^27 + 76*x^26 + 63*x^25 + 2*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 6*x^20 + 13*x^19 + 20*x^18 + 11*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 119*x^11 + 68*x^10 + 33*x^9 + 46*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 58*x^4 + 11*x^3 + 28*x^2 + 61*x + 78, x^95 + 15*x^93 + 30*x^92 + 53*x^91 + 124*x^90 + 51*x^89 + 106*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 126*x^84 + 9*x^83 + 100*x^82 + 47*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 115*x^75 + 52*x^74 + 5*x^73 + 86*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 50*x^68 + 119*x^67 + 44*x^66 + 113*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 105*x^27 + 44*x^26 + 31*x^25 + 18*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 54*x^20 + 109*x^19 + 52*x^18 + 43*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 87*x^11 + 100*x^10 + 65*x^9 + 30*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 10*x^4 + 43*x^3 + 124*x^2 + 29*x + 62, x^95 + 15*x^93 + 22*x^92 + 69*x^91 + 12*x^90 + 67*x^89 + 18*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 118*x^84 + 57*x^83 + 84*x^82 + 95*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 35*x^75 + 100*x^74 + 53*x^73 + 46*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 122*x^68 + 7*x^67 + 124*x^66 + x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 57*x^27 + 124*x^26 + 111*x^25 + 90*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 14*x^20 + 93*x^19 + 100*x^18 + 27*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 71*x^11 + 84*x^10 + 49*x^9 + 22*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 50*x^4 + 123*x^3 + 12*x^2 + 109*x + 54, x^95 + 15*x^93 + 110*x^92 + 21*x^91 + 28*x^90 + 83*x^89 + 90*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 78*x^84 + 41*x^83 + 68*x^82 + 15*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 19*x^75 + 20*x^74 + 101*x^73 + 102*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 98*x^68 + 87*x^67 + 76*x^66 + 17*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 73*x^27 + 76*x^26 + 63*x^25 + 66*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 70*x^20 + 13*x^19 + 20*x^18 + 11*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 119*x^11 + 68*x^10 + 33*x^9 + 110*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 122*x^4 + 11*x^3 + 28*x^2 + 61*x + 14, x^95 + 15*x^93 + 6*x^92 + 117*x^91 + 124*x^90 + 83*x^89 + 82*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 6*x^84 + 73*x^83 + 36*x^82 + 15*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 51*x^75 + 52*x^74 + 101*x^73 + 46*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 42*x^68 + 55*x^67 + 108*x^66 + 17*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 41*x^27 + 44*x^26 + 63*x^25 + 26*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 94*x^20 + 45*x^19 + 116*x^18 + 11*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 23*x^11 + 100*x^10 + 33*x^9 + 22*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 34*x^4 + 107*x^3 + 60*x^2 + 61*x + 86, x^95 + 15*x^93 + 82*x^92 + 85*x^91 + 68*x^90 + 19*x^89 + 6*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 50*x^84 + 105*x^83 + 92*x^82 + 79*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 83*x^75 + 12*x^74 + 37*x^73 + 58*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 30*x^68 + 23*x^67 + 20*x^66 + 81*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 9*x^27 + 20*x^26 + 127*x^25 + 30*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 58*x^20 + 77*x^19 + 12*x^18 + 75*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 55*x^11 + 92*x^10 + 97*x^9 + 50*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 6*x^4 + 75*x^3 + 68*x^2 + 125*x + 82, x^95 + 15*x^93 + 18*x^92 + 5*x^91 + 84*x^90 + 99*x^89 + 118*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 18*x^84 + 121*x^83 + 12*x^82 + 63*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 99*x^75 + 60*x^74 + 21*x^73 + 10*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 126*x^68 + 71*x^67 + 36*x^66 + 33*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 121*x^27 + 100*x^26 + 15*x^25 + 78*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 26*x^20 + 29*x^19 + 124*x^18 + 123*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 7*x^11 + 76*x^10 + 17*x^9 + 66*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 102*x^4 + 59*x^3 + 20*x^2 + 13*x + 2, x^95 + 15*x^93 + 90*x^92 + 37*x^91 + 20*x^90 + 35*x^89 + 62*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 122*x^84 + 89*x^83 + 12*x^82 + 127*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 67*x^75 + 124*x^74 + 85*x^73 + 2*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 22*x^68 + 103*x^67 + 36*x^66 + 97*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 25*x^27 + 36*x^26 + 79*x^25 + 54*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 34*x^20 + 125*x^19 + 124*x^18 + 59*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 103*x^11 + 12*x^10 + 81*x^9 + 90*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 30*x^4 + 91*x^3 + 20*x^2 + 77*x + 58, x^95 + 15*x^93 + 2*x^92 + 5*x^91 + 116*x^90 + 35*x^89 + 70*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 2*x^84 + 121*x^83 + 108*x^82 + 127*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 99*x^75 + 28*x^74 + 85*x^73 + 58*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 14*x^68 + 71*x^67 + 68*x^66 + 97*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 121*x^27 + 4*x^26 + 79*x^25 + 94*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 74*x^20 + 29*x^19 + 92*x^18 + 59*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 7*x^11 + 44*x^10 + 81*x^9 + 50*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 54*x^4 + 59*x^3 + 52*x^2 + 77*x + 114, x^95 + 15*x^93 + 110*x^92 + 69*x^91 + 76*x^90 + 99*x^89 + 42*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 46*x^84 + 57*x^83 + 84*x^82 + 63*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 35*x^75 + 36*x^74 + 21*x^73 + 86*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 66*x^68 + 7*x^67 + 124*x^66 + 33*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 57*x^27 + 60*x^26 + 15*x^25 + 82*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 38*x^20 + 93*x^19 + 100*x^18 + 123*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 71*x^11 + 20*x^10 + 17*x^9 + 30*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 90*x^4 + 123*x^3 + 12*x^2 + 13*x + 30, x^95 + 15*x^93 + 26*x^92 + 37*x^91 + 84*x^90 + 35*x^89 + 62*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 58*x^84 + 89*x^83 + 76*x^82 + 127*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 67*x^75 + 60*x^74 + 85*x^73 + 2*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 86*x^68 + 103*x^67 + 100*x^66 + 97*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 25*x^27 + 100*x^26 + 79*x^25 + 54*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 98*x^20 + 125*x^19 + 60*x^18 + 59*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 103*x^11 + 76*x^10 + 81*x^9 + 90*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 94*x^4 + 91*x^3 + 84*x^2 + 77*x + 58, x^95 + 15*x^93 + 30*x^92 + 85*x^91 + 124*x^90 + 83*x^89 + 42*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 126*x^84 + 105*x^83 + 100*x^82 + 15*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 83*x^75 + 52*x^74 + 101*x^73 + 22*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 50*x^68 + 23*x^67 + 44*x^66 + 17*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 9*x^27 + 44*x^26 + 63*x^25 + 82*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 54*x^20 + 77*x^19 + 52*x^18 + 11*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 55*x^11 + 100*x^10 + 33*x^9 + 94*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 10*x^4 + 75*x^3 + 124*x^2 + 61*x + 126, x^95 + 15*x^93 + 30*x^92 + 101*x^91 + 76*x^90 + 67*x^89 + 26*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 30*x^84 + 25*x^83 + 84*x^82 + 95*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 3*x^75 + 36*x^74 + 53*x^73 + 102*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 82*x^68 + 39*x^67 + 124*x^66 + x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 89*x^27 + 60*x^26 + 111*x^25 + 2*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 86*x^20 + 61*x^19 + 100*x^18 + 27*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 39*x^11 + 20*x^10 + 49*x^9 + 110*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 42*x^4 + 27*x^3 + 12*x^2 + 109*x + 46, x^95 + 15*x^93 + 10*x^92 + 21*x^91 + 100*x^90 + 115*x^89 + 94*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 10*x^84 + 41*x^83 + 124*x^82 + 111*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 19*x^75 + 108*x^74 + 69*x^73 + 34*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 70*x^68 + 87*x^67 + 116*x^66 + 49*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 73*x^27 + 52*x^26 + 95*x^25 + 86*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 114*x^20 + 13*x^19 + 44*x^18 + 107*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 119*x^11 + 60*x^10 + x^9 + 122*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 14*x^4 + 11*x^3 + 36*x^2 + 93*x + 58, x^95 + 15*x^93 + 82*x^92 + 101*x^91 + 20*x^90 + 3*x^89 + 118*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 82*x^84 + 25*x^83 + 76*x^82 + 31*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 3*x^75 + 124*x^74 + 117*x^73 + 10*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 62*x^68 + 39*x^67 + 100*x^66 + 65*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 89*x^27 + 36*x^26 + 47*x^25 + 78*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 90*x^20 + 61*x^19 + 60*x^18 + 91*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 39*x^11 + 12*x^10 + 113*x^9 + 66*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 38*x^4 + 27*x^3 + 84*x^2 + 45*x + 2, x^95 + 15*x^93 + 22*x^92 + 21*x^91 + 28*x^90 + 51*x^89 + 2*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 22*x^84 + 41*x^83 + 4*x^82 + 47*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 19*x^75 + 20*x^74 + 5*x^73 + 126*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 26*x^68 + 87*x^67 + 12*x^66 + 113*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 73*x^27 + 76*x^26 + 31*x^25 + 10*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 46*x^20 + 13*x^19 + 84*x^18 + 43*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 119*x^11 + 68*x^10 + 65*x^9 + 38*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 82*x^4 + 11*x^3 + 92*x^2 + 29*x + 102, x^95 + 15*x^93 + 46*x^92 + 21*x^91 + 92*x^90 + 83*x^89 + 90*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 14*x^84 + 41*x^83 + 4*x^82 + 15*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 19*x^75 + 84*x^74 + 101*x^73 + 102*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 34*x^68 + 87*x^67 + 12*x^66 + 17*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 73*x^27 + 12*x^26 + 63*x^25 + 66*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 6*x^20 + 13*x^19 + 84*x^18 + 11*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 119*x^11 + 4*x^10 + 33*x^9 + 110*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 58*x^4 + 11*x^3 + 92*x^2 + 61*x + 14, x^95 + 15*x^93 + 2*x^92 + 69*x^91 + 20*x^90 + 35*x^89 + 102*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 66*x^84 + 57*x^83 + 76*x^82 + 127*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 35*x^75 + 124*x^74 + 85*x^73 + 26*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 78*x^68 + 7*x^67 + 100*x^66 + 97*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 57*x^27 + 36*x^26 + 79*x^25 + 126*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 10*x^20 + 93*x^19 + 60*x^18 + 59*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 71*x^11 + 12*x^10 + 81*x^9 + 18*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 118*x^4 + 123*x^3 + 84*x^2 + 77*x + 18, x^95 + 15*x^93 + 74*x^92 + 101*x^91 + 84*x^90 + 35*x^89 + 110*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 42*x^84 + 25*x^83 + 76*x^82 + 127*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 3*x^75 + 60*x^74 + 85*x^73 + 82*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 102*x^68 + 39*x^67 + 100*x^66 + 97*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 89*x^27 + 100*x^26 + 79*x^25 + 38*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 18*x^20 + 61*x^19 + 60*x^18 + 59*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 39*x^11 + 76*x^10 + 81*x^9 + 106*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 46*x^4 + 27*x^3 + 84*x^2 + 77*x + 10, x^95 + 15*x^93 + 126*x^92 + 53*x^91 + 28*x^90 + 51*x^89 + 42*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 30*x^84 + 9*x^83 + 68*x^82 + 47*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 115*x^75 + 20*x^74 + 5*x^73 + 22*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 18*x^68 + 119*x^67 + 76*x^66 + 113*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 105*x^27 + 76*x^26 + 31*x^25 + 82*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 86*x^20 + 109*x^19 + 20*x^18 + 43*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 87*x^11 + 68*x^10 + 65*x^9 + 94*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 106*x^4 + 43*x^3 + 28*x^2 + 29*x + 62, x^95 + 15*x^93 + 2*x^92 + 37*x^91 + 20*x^90 + 3*x^89 + 38*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 66*x^84 + 89*x^83 + 76*x^82 + 31*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 67*x^75 + 124*x^74 + 117*x^73 + 90*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 78*x^68 + 103*x^67 + 100*x^66 + 65*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 25*x^27 + 36*x^26 + 47*x^25 + 62*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 10*x^20 + 125*x^19 + 60*x^18 + 91*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 103*x^11 + 12*x^10 + 113*x^9 + 82*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 118*x^4 + 91*x^3 + 84*x^2 + 45*x + 82, x^95 + 15*x^93 + 38*x^92 + 53*x^91 + 124*x^90 + 83*x^89 + 50*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 38*x^84 + 9*x^83 + 36*x^82 + 15*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 115*x^75 + 52*x^74 + 101*x^73 + 78*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 10*x^68 + 119*x^67 + 108*x^66 + 17*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 105*x^27 + 44*x^26 + 63*x^25 + 122*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 126*x^20 + 109*x^19 + 116*x^18 + 11*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 87*x^11 + 100*x^10 + 33*x^9 + 54*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 2*x^4 + 43*x^3 + 60*x^2 + 61*x + 118, x^95 + 15*x^93 + 58*x^92 + 37*x^91 + 20*x^90 + 99*x^89 + 94*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 90*x^84 + 89*x^83 + 12*x^82 + 63*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 67*x^75 + 124*x^74 + 21*x^73 + 98*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 54*x^68 + 103*x^67 + 36*x^66 + 33*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 25*x^27 + 36*x^26 + 15*x^25 + 86*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 2*x^20 + 125*x^19 + 124*x^18 + 123*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 103*x^11 + 12*x^10 + 17*x^9 + 58*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 62*x^4 + 91*x^3 + 20*x^2 + 13*x + 26, x^95 + 15*x^93 + 50*x^92 + 69*x^91 + 116*x^90 + 99*x^89 + 54*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 114*x^84 + 57*x^83 + 108*x^82 + 63*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 35*x^75 + 28*x^74 + 21*x^73 + 74*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 30*x^68 + 7*x^67 + 68*x^66 + 33*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 57*x^27 + 4*x^26 + 15*x^25 + 14*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 122*x^20 + 93*x^19 + 92*x^18 + 123*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 71*x^11 + 44*x^10 + 17*x^9 + 2*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 6*x^4 + 123*x^3 + 52*x^2 + 13*x + 2, x^95 + 15*x^93 + 6*x^92 + 21*x^91 + 28*x^90 + 115*x^89 + 114*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 70*x^84 + 41*x^83 + 4*x^82 + 111*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 19*x^75 + 20*x^74 + 69*x^73 + 14*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 106*x^68 + 87*x^67 + 12*x^66 + 49*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 73*x^27 + 76*x^26 + 95*x^25 + 58*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 30*x^20 + 13*x^19 + 84*x^18 + 107*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 119*x^11 + 68*x^10 + x^9 + 118*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 98*x^4 + 11*x^3 + 92*x^2 + 93*x + 118, x^95 + 15*x^93 + 90*x^92 + 117*x^91 + 68*x^90 + 83*x^89 + 78*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 90*x^84 + 73*x^83 + 28*x^82 + 15*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 51*x^75 + 12*x^74 + 101*x^73 + 50*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 118*x^68 + 55*x^67 + 84*x^66 + 17*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 41*x^27 + 20*x^26 + 63*x^25 + 6*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 2*x^20 + 45*x^19 + 76*x^18 + 11*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 23*x^11 + 92*x^10 + 33*x^9 + 74*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 126*x^4 + 107*x^3 + 4*x^2 + 61*x + 10, x^95 + 15*x^93 + 102*x^92 + 85*x^91 + 28*x^90 + 51*x^89 + 82*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 38*x^84 + 105*x^83 + 4*x^82 + 47*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 83*x^75 + 20*x^74 + 5*x^73 + 46*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 10*x^68 + 23*x^67 + 12*x^66 + 113*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 9*x^27 + 76*x^26 + 31*x^25 + 26*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 126*x^20 + 77*x^19 + 84*x^18 + 43*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 55*x^11 + 68*x^10 + 65*x^9 + 22*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 2*x^4 + 75*x^3 + 92*x^2 + 29*x + 22, x^95 + 15*x^93 + 78*x^92 + 37*x^91 + 44*x^90 + 3*x^89 + 42*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 78*x^84 + 89*x^83 + 116*x^82 + 31*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 67*x^75 + 68*x^74 + 117*x^73 + 86*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 34*x^68 + 103*x^67 + 92*x^66 + 65*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 25*x^27 + 28*x^26 + 47*x^25 + 82*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 70*x^20 + 125*x^19 + 4*x^18 + 91*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 103*x^11 + 52*x^10 + 113*x^9 + 30*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 58*x^4 + 91*x^3 + 108*x^2 + 45*x + 94, x^95 + 15*x^93 + 98*x^92 + 101*x^91 + 84*x^90 + 3*x^89 + 6*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 34*x^84 + 25*x^83 + 12*x^82 + 31*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 3*x^75 + 60*x^74 + 117*x^73 + 122*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 110*x^68 + 39*x^67 + 36*x^66 + 65*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 89*x^27 + 100*x^26 + 47*x^25 + 30*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 106*x^20 + 61*x^19 + 124*x^18 + 91*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 39*x^11 + 76*x^10 + 113*x^9 + 114*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 22*x^4 + 27*x^3 + 20*x^2 + 45*x + 114, x^95 + 15*x^93 + 90*x^92 + 69*x^91 + 52*x^90 + 67*x^89 + 94*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 58*x^84 + 57*x^83 + 108*x^82 + 95*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 35*x^75 + 92*x^74 + 53*x^73 + 98*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 86*x^68 + 7*x^67 + 68*x^66 + x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 57*x^27 + 68*x^26 + 111*x^25 + 86*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 98*x^20 + 93*x^19 + 92*x^18 + 27*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 71*x^11 + 108*x^10 + 49*x^9 + 58*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 94*x^4 + 123*x^3 + 52*x^2 + 109*x + 90, x^95 + 15*x^93 + 34*x^92 + 117*x^91 + 4*x^90 + 51*x^89 + 22*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 66*x^84 + 73*x^83 + 28*x^82 + 47*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 51*x^75 + 76*x^74 + 5*x^73 + 42*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 14*x^68 + 55*x^67 + 84*x^66 + 113*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 41*x^27 + 84*x^26 + 31*x^25 + 110*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 10*x^20 + 45*x^19 + 76*x^18 + 43*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 23*x^11 + 28*x^10 + 65*x^9 + 98*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 54*x^4 + 107*x^3 + 4*x^2 + 29*x + 66, x^95 + 15*x^93 + 26*x^92 + 85*x^91 + 36*x^90 + 115*x^89 + 46*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 90*x^84 + 105*x^83 + 60*x^82 + 111*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 83*x^75 + 44*x^74 + 69*x^73 + 82*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 118*x^68 + 23*x^67 + 52*x^66 + 49*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 9*x^27 + 116*x^26 + 95*x^25 + 102*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 2*x^20 + 77*x^19 + 108*x^18 + 107*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 55*x^11 + 124*x^10 + x^9 + 106*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 126*x^4 + 75*x^3 + 100*x^2 + 93*x + 106, x^95 + 15*x^93 + 30*x^92 + 21*x^91 + 124*x^90 + 19*x^89 + 42*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 126*x^84 + 41*x^83 + 100*x^82 + 79*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 19*x^75 + 52*x^74 + 37*x^73 + 22*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 50*x^68 + 87*x^67 + 44*x^66 + 81*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 73*x^27 + 44*x^26 + 127*x^25 + 82*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 54*x^20 + 13*x^19 + 52*x^18 + 75*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 119*x^11 + 100*x^10 + 97*x^9 + 94*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 10*x^4 + 11*x^3 + 124*x^2 + 125*x + 126, x^95 + 15*x^93 + 114*x^92 + 5*x^91 + 20*x^90 + 99*x^89 + 22*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 114*x^84 + 121*x^83 + 76*x^82 + 63*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 99*x^75 + 124*x^74 + 21*x^73 + 106*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 30*x^68 + 71*x^67 + 100*x^66 + 33*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 121*x^27 + 36*x^26 + 15*x^25 + 110*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 122*x^20 + 29*x^19 + 60*x^18 + 123*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 7*x^11 + 12*x^10 + 17*x^9 + 34*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 6*x^4 + 59*x^3 + 84*x^2 + 13*x + 98, x^95 + 15*x^93 + 50*x^92 + 21*x^91 + 100*x^90 + 83*x^89 + 70*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 82*x^84 + 41*x^83 + 60*x^82 + 15*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 19*x^75 + 108*x^74 + 101*x^73 + 122*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 126*x^68 + 87*x^67 + 52*x^66 + 17*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 73*x^27 + 52*x^26 + 63*x^25 + 94*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 90*x^20 + 13*x^19 + 108*x^18 + 11*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 119*x^11 + 60*x^10 + 33*x^9 + 114*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 102*x^4 + 11*x^3 + 100*x^2 + 61*x + 82, x^95 + 15*x^93 + 78*x^92 + 21*x^91 + 92*x^90 + 19*x^89 + 58*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 46*x^84 + 41*x^83 + 4*x^82 + 79*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 19*x^75 + 84*x^74 + 37*x^73 + 6*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 2*x^68 + 87*x^67 + 12*x^66 + 81*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 73*x^27 + 12*x^26 + 127*x^25 + 34*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 38*x^20 + 13*x^19 + 84*x^18 + 75*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 119*x^11 + 4*x^10 + 97*x^9 + 14*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 26*x^4 + 11*x^3 + 92*x^2 + 125*x + 46, x^95 + 15*x^93 + 106*x^92 + 21*x^91 + 4*x^90 + 115*x^89 + 30*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 42*x^84 + 41*x^83 + 92*x^82 + 111*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 19*x^75 + 76*x^74 + 69*x^73 + 98*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 38*x^68 + 87*x^67 + 20*x^66 + 49*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 73*x^27 + 84*x^26 + 95*x^25 + 22*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 18*x^20 + 13*x^19 + 12*x^18 + 107*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 119*x^11 + 28*x^10 + x^9 + 58*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 110*x^4 + 11*x^3 + 68*x^2 + 93*x + 58, x^95 + 15*x^93 + 2*x^92 + 53*x^91 + 36*x^90 + 115*x^89 + 86*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 98*x^84 + 9*x^83 + 124*x^82 + 111*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 115*x^75 + 44*x^74 + 69*x^73 + 106*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 110*x^68 + 119*x^67 + 116*x^66 + 49*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 105*x^27 + 116*x^26 + 95*x^25 + 46*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 42*x^20 + 109*x^19 + 44*x^18 + 107*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 87*x^11 + 124*x^10 + x^9 + 34*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 22*x^4 + 43*x^3 + 36*x^2 + 93*x + 66, x^95 + 15*x^93 + 90*x^92 + 101*x^91 + 84*x^90 + 35*x^89 + 62*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 122*x^84 + 25*x^83 + 76*x^82 + 127*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 3*x^75 + 60*x^74 + 85*x^73 + 2*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 22*x^68 + 39*x^67 + 100*x^66 + 97*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 89*x^27 + 100*x^26 + 79*x^25 + 54*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 34*x^20 + 61*x^19 + 60*x^18 + 59*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 39*x^11 + 76*x^10 + 81*x^9 + 90*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 30*x^4 + 27*x^3 + 84*x^2 + 77*x + 58, x^95 + 15*x^93 + 106*x^92 + 117*x^91 + 4*x^90 + 83*x^89 + 94*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 42*x^84 + 73*x^83 + 92*x^82 + 15*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 51*x^75 + 76*x^74 + 101*x^73 + 34*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 38*x^68 + 55*x^67 + 20*x^66 + 17*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 41*x^27 + 84*x^26 + 63*x^25 + 86*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 18*x^20 + 45*x^19 + 12*x^18 + 11*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 23*x^11 + 28*x^10 + 33*x^9 + 122*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 110*x^4 + 107*x^3 + 68*x^2 + 61*x + 122, x^95 + 15*x^93 + 2*x^92 + 21*x^91 + 100*x^90 + 19*x^89 + 22*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 98*x^84 + 41*x^83 + 60*x^82 + 79*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 19*x^75 + 108*x^74 + 37*x^73 + 42*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 110*x^68 + 87*x^67 + 52*x^66 + 81*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 73*x^27 + 52*x^26 + 127*x^25 + 110*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 42*x^20 + 13*x^19 + 108*x^18 + 75*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 119*x^11 + 60*x^10 + 97*x^9 + 98*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 22*x^4 + 11*x^3 + 100*x^2 + 125*x + 2, x^95 + 15*x^93 + 50*x^92 + 117*x^91 + 100*x^90 + 115*x^89 + 70*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 82*x^84 + 73*x^83 + 60*x^82 + 111*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 51*x^75 + 108*x^74 + 69*x^73 + 122*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 126*x^68 + 55*x^67 + 52*x^66 + 49*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 41*x^27 + 52*x^26 + 95*x^25 + 94*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 90*x^20 + 45*x^19 + 108*x^18 + 107*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 23*x^11 + 60*x^10 + x^9 + 114*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 102*x^4 + 107*x^3 + 100*x^2 + 93*x + 82, x^95 + 15*x^93 + 30*x^92 + 69*x^91 + 76*x^90 + 35*x^89 + 90*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 30*x^84 + 57*x^83 + 84*x^82 + 127*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 35*x^75 + 36*x^74 + 85*x^73 + 38*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 82*x^68 + 7*x^67 + 124*x^66 + 97*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 57*x^27 + 60*x^26 + 79*x^25 + 66*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 86*x^20 + 93*x^19 + 100*x^18 + 59*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 71*x^11 + 20*x^10 + 81*x^9 + 46*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 42*x^4 + 123*x^3 + 12*x^2 + 77*x + 110, x^95 + 15*x^93 + 42*x^92 + 69*x^91 + 52*x^90 + 67*x^89 + 110*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 74*x^84 + 57*x^83 + 108*x^82 + 95*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 35*x^75 + 92*x^74 + 53*x^73 + 82*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 70*x^68 + 7*x^67 + 68*x^66 + x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 57*x^27 + 68*x^26 + 111*x^25 + 38*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 50*x^20 + 93*x^19 + 92*x^18 + 27*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 71*x^11 + 108*x^10 + 49*x^9 + 106*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 14*x^4 + 123*x^3 + 52*x^2 + 109*x + 74, x^95 + 15*x^93 + 78*x^92 + 101*x^91 + 44*x^90 + 67*x^89 + 42*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 78*x^84 + 25*x^83 + 116*x^82 + 95*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 3*x^75 + 68*x^74 + 53*x^73 + 86*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 34*x^68 + 39*x^67 + 92*x^66 + x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 89*x^27 + 28*x^26 + 111*x^25 + 82*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 70*x^20 + 61*x^19 + 4*x^18 + 27*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 39*x^11 + 52*x^10 + 49*x^9 + 30*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 58*x^4 + 27*x^3 + 108*x^2 + 109*x + 94, x^95 + 15*x^93 + 34*x^92 + 21*x^91 + 68*x^90 + 83*x^89 + 22*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 66*x^84 + 41*x^83 + 92*x^82 + 15*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 19*x^75 + 12*x^74 + 101*x^73 + 42*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 14*x^68 + 87*x^67 + 20*x^66 + 17*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 73*x^27 + 20*x^26 + 63*x^25 + 110*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 10*x^20 + 13*x^19 + 12*x^18 + 11*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 119*x^11 + 92*x^10 + 33*x^9 + 98*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 54*x^4 + 11*x^3 + 68*x^2 + 61*x + 66, x^95 + 15*x^93 + 38*x^92 + 117*x^91 + 92*x^90 + 83*x^89 + 18*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 102*x^84 + 73*x^83 + 68*x^82 + 15*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 51*x^75 + 84*x^74 + 101*x^73 + 110*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 74*x^68 + 55*x^67 + 76*x^66 + 17*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 41*x^27 + 12*x^26 + 63*x^25 + 90*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 62*x^20 + 45*x^19 + 20*x^18 + 11*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 23*x^11 + 4*x^10 + 33*x^9 + 86*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 66*x^4 + 107*x^3 + 28*x^2 + 61*x + 86, x^95 + 15*x^93 + 26*x^92 + 53*x^91 + 36*x^90 + 83*x^89 + 110*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 90*x^84 + 9*x^83 + 60*x^82 + 15*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 115*x^75 + 44*x^74 + 101*x^73 + 18*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 118*x^68 + 119*x^67 + 52*x^66 + 17*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 105*x^27 + 116*x^26 + 63*x^25 + 38*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 2*x^20 + 109*x^19 + 108*x^18 + 11*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 87*x^11 + 124*x^10 + 33*x^9 + 42*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 126*x^4 + 43*x^3 + 100*x^2 + 61*x + 42, x^95 + 15*x^93 + 50*x^92 + 53*x^91 + 4*x^90 + 115*x^89 + 102*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 18*x^84 + 9*x^83 + 28*x^82 + 111*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 115*x^75 + 76*x^74 + 69*x^73 + 90*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 62*x^68 + 119*x^67 + 84*x^66 + 49*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 105*x^27 + 84*x^26 + 95*x^25 + 126*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 26*x^20 + 109*x^19 + 76*x^18 + 107*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 87*x^11 + 28*x^10 + x^9 + 82*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 38*x^4 + 43*x^3 + 4*x^2 + 93*x + 114, x^95 + 15*x^93 + 34*x^92 + 101*x^91 + 116*x^90 + 3*x^89 + 38*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 34*x^84 + 25*x^83 + 108*x^82 + 31*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 3*x^75 + 28*x^74 + 117*x^73 + 90*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 110*x^68 + 39*x^67 + 68*x^66 + 65*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 89*x^27 + 4*x^26 + 47*x^25 + 62*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 106*x^20 + 61*x^19 + 92*x^18 + 91*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 39*x^11 + 44*x^10 + 113*x^9 + 82*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 22*x^4 + 27*x^3 + 52*x^2 + 45*x + 18, x^95 + 15*x^93 + 30*x^92 + 21*x^91 + 28*x^90 + 19*x^89 + 10*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 62*x^84 + 41*x^83 + 68*x^82 + 79*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 19*x^75 + 20*x^74 + 37*x^73 + 54*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 114*x^68 + 87*x^67 + 76*x^66 + 81*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 73*x^27 + 76*x^26 + 127*x^25 + 50*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 118*x^20 + 13*x^19 + 20*x^18 + 75*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 119*x^11 + 68*x^10 + 97*x^9 + 126*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 74*x^4 + 11*x^3 + 28*x^2 + 125*x + 94, x^95 + 15*x^93 + 34*x^92 + 69*x^91 + 84*x^90 + 35*x^89 + 70*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 98*x^84 + 57*x^83 + 12*x^82 + 127*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 35*x^75 + 60*x^74 + 85*x^73 + 58*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 46*x^68 + 7*x^67 + 36*x^66 + 97*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 57*x^27 + 100*x^26 + 79*x^25 + 94*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 42*x^20 + 93*x^19 + 124*x^18 + 59*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 71*x^11 + 76*x^10 + 81*x^9 + 50*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 86*x^4 + 123*x^3 + 20*x^2 + 77*x + 50, x^95 + 15*x^93 + 38*x^92 + 5*x^91 + 108*x^90 + 67*x^89 + 66*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 6*x^84 + 121*x^83 + 116*x^82 + 95*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 99*x^75 + 4*x^74 + 53*x^73 + 126*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 106*x^68 + 71*x^67 + 92*x^66 + x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 121*x^27 + 92*x^26 + 111*x^25 + 74*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 94*x^20 + 29*x^19 + 4*x^18 + 27*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 7*x^11 + 116*x^10 + 49*x^9 + 38*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 98*x^4 + 59*x^3 + 108*x^2 + 109*x + 70, x^95 + 15*x^93 + 38*x^92 + 37*x^91 + 44*x^90 + 35*x^89 + 2*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 6*x^84 + 89*x^83 + 52*x^82 + 127*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 67*x^75 + 68*x^74 + 85*x^73 + 62*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 106*x^68 + 103*x^67 + 28*x^66 + 97*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 25*x^27 + 28*x^26 + 79*x^25 + 10*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 94*x^20 + 125*x^19 + 68*x^18 + 59*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 103*x^11 + 52*x^10 + 81*x^9 + 102*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 98*x^4 + 91*x^3 + 44*x^2 + 77*x + 6, x^95 + 15*x^93 + 34*x^92 + 53*x^91 + 68*x^90 + 115*x^89 + 86*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 66*x^84 + 9*x^83 + 92*x^82 + 111*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 115*x^75 + 12*x^74 + 69*x^73 + 106*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 14*x^68 + 119*x^67 + 20*x^66 + 49*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 105*x^27 + 20*x^26 + 95*x^25 + 46*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 10*x^20 + 109*x^19 + 12*x^18 + 107*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 87*x^11 + 92*x^10 + x^9 + 34*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 54*x^4 + 43*x^3 + 68*x^2 + 93*x + 2, x^95 + 15*x^93 + 46*x^92 + 37*x^91 + 76*x^90 + 3*x^89 + 106*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 110*x^84 + 89*x^83 + 84*x^82 + 31*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 67*x^75 + 36*x^74 + 117*x^73 + 22*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 2*x^68 + 103*x^67 + 124*x^66 + 65*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 25*x^27 + 60*x^26 + 47*x^25 + 18*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 102*x^20 + 125*x^19 + 100*x^18 + 91*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 103*x^11 + 20*x^10 + 113*x^9 + 94*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 26*x^4 + 91*x^3 + 12*x^2 + 45*x + 94, x^95 + 15*x^93 + 26*x^92 + 21*x^91 + 4*x^90 + 51*x^89 + 78*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 26*x^84 + 41*x^83 + 92*x^82 + 47*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 19*x^75 + 76*x^74 + 5*x^73 + 50*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 54*x^68 + 87*x^67 + 20*x^66 + 113*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 73*x^27 + 84*x^26 + 31*x^25 + 6*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 66*x^20 + 13*x^19 + 12*x^18 + 43*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 119*x^11 + 28*x^10 + 65*x^9 + 74*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 62*x^4 + 11*x^3 + 68*x^2 + 29*x + 10, x^95 + 15*x^93 + 82*x^92 + 85*x^91 + 68*x^90 + 83*x^89 + 70*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 50*x^84 + 105*x^83 + 92*x^82 + 15*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 83*x^75 + 12*x^74 + 101*x^73 + 122*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 30*x^68 + 23*x^67 + 20*x^66 + 17*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 9*x^27 + 20*x^26 + 63*x^25 + 94*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 58*x^20 + 77*x^19 + 12*x^18 + 11*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 55*x^11 + 92*x^10 + 33*x^9 + 114*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 6*x^4 + 75*x^3 + 68*x^2 + 61*x + 18, x^95 + 15*x^93 + 110*x^92 + 117*x^91 + 60*x^90 + 115*x^89 + 58*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 14*x^84 + 73*x^83 + 36*x^82 + 111*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 51*x^75 + 116*x^74 + 69*x^73 + 6*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 34*x^68 + 55*x^67 + 108*x^66 + 49*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 41*x^27 + 108*x^26 + 95*x^25 + 34*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 6*x^20 + 45*x^19 + 116*x^18 + 107*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 23*x^11 + 36*x^10 + x^9 + 14*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 58*x^4 + 107*x^3 + 60*x^2 + 93*x + 110, x^95 + 15*x^93 + 90*x^92 + 5*x^91 + 116*x^90 + 67*x^89 + 94*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 58*x^84 + 121*x^83 + 44*x^82 + 95*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 99*x^75 + 28*x^74 + 53*x^73 + 98*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 86*x^68 + 71*x^67 + 4*x^66 + x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 121*x^27 + 4*x^26 + 111*x^25 + 86*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 98*x^20 + 29*x^19 + 28*x^18 + 27*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 7*x^11 + 44*x^10 + 49*x^9 + 58*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 94*x^4 + 59*x^3 + 116*x^2 + 109*x + 90, x^95 + 15*x^93 + 122*x^92 + 85*x^91 + 100*x^90 + 115*x^89 + 78*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 58*x^84 + 105*x^83 + 124*x^82 + 111*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 83*x^75 + 108*x^74 + 69*x^73 + 50*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 22*x^68 + 23*x^67 + 116*x^66 + 49*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 9*x^27 + 52*x^26 + 95*x^25 + 6*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 98*x^20 + 77*x^19 + 44*x^18 + 107*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 55*x^11 + 60*x^10 + x^9 + 74*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 30*x^4 + 75*x^3 + 36*x^2 + 93*x + 74, x^95 + 15*x^93 + 82*x^92 + 21*x^91 + 4*x^90 + 19*x^89 + 6*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 50*x^84 + 41*x^83 + 28*x^82 + 79*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 19*x^75 + 76*x^74 + 37*x^73 + 58*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 30*x^68 + 87*x^67 + 84*x^66 + 81*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 73*x^27 + 84*x^26 + 127*x^25 + 30*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 58*x^20 + 13*x^19 + 76*x^18 + 75*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 119*x^11 + 28*x^10 + 97*x^9 + 50*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 6*x^4 + 11*x^3 + 4*x^2 + 125*x + 82, x^95 + 15*x^93 + 10*x^92 + 101*x^91 + 20*x^90 + 99*x^89 + 46*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 106*x^84 + 25*x^83 + 12*x^82 + 63*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 3*x^75 + 124*x^74 + 21*x^73 + 18*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 38*x^68 + 39*x^67 + 36*x^66 + 33*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 89*x^27 + 36*x^26 + 15*x^25 + 102*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 82*x^20 + 61*x^19 + 124*x^18 + 123*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 39*x^11 + 12*x^10 + 17*x^9 + 42*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 110*x^4 + 27*x^3 + 20*x^2 + 13*x + 74, x^95 + 15*x^93 + 38*x^92 + 37*x^91 + 108*x^90 + 99*x^89 + 2*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 6*x^84 + 89*x^83 + 116*x^82 + 63*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 67*x^75 + 4*x^74 + 21*x^73 + 62*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 106*x^68 + 103*x^67 + 92*x^66 + 33*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 25*x^27 + 92*x^26 + 15*x^25 + 10*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 94*x^20 + 125*x^19 + 4*x^18 + 123*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 103*x^11 + 116*x^10 + 17*x^9 + 102*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 98*x^4 + 91*x^3 + 108*x^2 + 13*x + 6, x^95 + 15*x^93 + 14*x^92 + 5*x^91 + 76*x^90 + 35*x^89 + 74*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 78*x^84 + 121*x^83 + 84*x^82 + 127*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 99*x^75 + 36*x^74 + 85*x^73 + 54*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 34*x^68 + 71*x^67 + 124*x^66 + 97*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 121*x^27 + 60*x^26 + 79*x^25 + 114*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 70*x^20 + 29*x^19 + 100*x^18 + 59*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 7*x^11 + 20*x^10 + 81*x^9 + 126*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 58*x^4 + 59*x^3 + 12*x^2 + 77*x + 126, x^95 + 15*x^93 + 58*x^92 + 117*x^91 + 4*x^90 + 83*x^89 + 110*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 58*x^84 + 73*x^83 + 92*x^82 + 15*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 51*x^75 + 76*x^74 + 101*x^73 + 18*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 22*x^68 + 55*x^67 + 20*x^66 + 17*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 41*x^27 + 84*x^26 + 63*x^25 + 38*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 98*x^20 + 45*x^19 + 12*x^18 + 11*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 23*x^11 + 28*x^10 + 33*x^9 + 42*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 30*x^4 + 107*x^3 + 68*x^2 + 61*x + 106, x^95 + 15*x^93 + 58*x^92 + 69*x^91 + 84*x^90 + 67*x^89 + 30*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 90*x^84 + 57*x^83 + 76*x^82 + 95*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 35*x^75 + 60*x^74 + 53*x^73 + 34*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 54*x^68 + 7*x^67 + 100*x^66 + x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 57*x^27 + 100*x^26 + 111*x^25 + 22*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 2*x^20 + 93*x^19 + 60*x^18 + 27*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 71*x^11 + 76*x^10 + 49*x^9 + 122*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 62*x^4 + 123*x^3 + 84*x^2 + 109*x + 90, x^95 + 15*x^93 + 118*x^92 + 101*x^91 + 44*x^90 + 99*x^89 + 18*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 22*x^84 + 25*x^83 + 52*x^82 + 63*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 3*x^75 + 68*x^74 + 21*x^73 + 46*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 90*x^68 + 39*x^67 + 28*x^66 + 33*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 89*x^27 + 28*x^26 + 15*x^25 + 90*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 46*x^20 + 61*x^19 + 68*x^18 + 123*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 39*x^11 + 52*x^10 + 17*x^9 + 22*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 18*x^4 + 27*x^3 + 44*x^2 + 13*x + 118, x^95 + 15*x^93 + 54*x^92 + 37*x^91 + 12*x^90 + 99*x^89 + 50*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 22*x^84 + 89*x^83 + 84*x^82 + 63*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 67*x^75 + 100*x^74 + 21*x^73 + 14*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 90*x^68 + 103*x^67 + 124*x^66 + 33*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 25*x^27 + 124*x^26 + 15*x^25 + 122*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 46*x^20 + 125*x^19 + 100*x^18 + 123*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 103*x^11 + 84*x^10 + 17*x^9 + 118*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 18*x^4 + 91*x^3 + 12*x^2 + 13*x + 22, x^95 + 15*x^93 + 58*x^92 + 69*x^91 + 116*x^90 + 67*x^89 + 126*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 26*x^84 + 57*x^83 + 44*x^82 + 95*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 35*x^75 + 28*x^74 + 53*x^73 + 66*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 118*x^68 + 7*x^67 + 4*x^66 + x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 57*x^27 + 4*x^26 + 111*x^25 + 118*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 66*x^20 + 93*x^19 + 28*x^18 + 27*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 71*x^11 + 44*x^10 + 49*x^9 + 26*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 126*x^4 + 123*x^3 + 116*x^2 + 109*x + 58, x^95 + 15*x^93 + 62*x^92 + 5*x^91 + 44*x^90 + 35*x^89 + 90*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 126*x^84 + 121*x^83 + 116*x^82 + 127*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 99*x^75 + 68*x^74 + 85*x^73 + 38*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 114*x^68 + 71*x^67 + 92*x^66 + 97*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 121*x^27 + 28*x^26 + 79*x^25 + 66*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 54*x^20 + 29*x^19 + 4*x^18 + 59*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 7*x^11 + 52*x^10 + 81*x^9 + 46*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 74*x^4 + 59*x^3 + 108*x^2 + 77*x + 46, x^95 + 15*x^93 + 114*x^92 + 53*x^91 + 100*x^90 + 51*x^89 + 6*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 18*x^84 + 9*x^83 + 60*x^82 + 47*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 115*x^75 + 108*x^74 + 5*x^73 + 58*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 62*x^68 + 119*x^67 + 52*x^66 + 113*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 105*x^27 + 52*x^26 + 31*x^25 + 30*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 26*x^20 + 109*x^19 + 108*x^18 + 43*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 87*x^11 + 60*x^10 + 65*x^9 + 50*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 38*x^4 + 43*x^3 + 100*x^2 + 29*x + 18, x^95 + 15*x^93 + 46*x^92 + 101*x^91 + 76*x^90 + 67*x^89 + 106*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 110*x^84 + 25*x^83 + 84*x^82 + 95*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 3*x^75 + 36*x^74 + 53*x^73 + 22*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 2*x^68 + 39*x^67 + 124*x^66 + x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 89*x^27 + 60*x^26 + 111*x^25 + 18*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 102*x^20 + 61*x^19 + 100*x^18 + 27*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 39*x^11 + 20*x^10 + 49*x^9 + 94*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 26*x^4 + 27*x^3 + 12*x^2 + 109*x + 94, x^95 + 15*x^93 + 82*x^92 + 37*x^91 + 20*x^90 + 67*x^89 + 118*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 82*x^84 + 89*x^83 + 76*x^82 + 95*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 67*x^75 + 124*x^74 + 53*x^73 + 10*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 62*x^68 + 103*x^67 + 100*x^66 + x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 25*x^27 + 36*x^26 + 111*x^25 + 78*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 90*x^20 + 125*x^19 + 60*x^18 + 27*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 103*x^11 + 12*x^10 + 49*x^9 + 66*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 38*x^4 + 91*x^3 + 84*x^2 + 109*x + 2, x^95 + 15*x^93 + 110*x^92 + 37*x^91 + 76*x^90 + 3*x^89 + 42*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 46*x^84 + 89*x^83 + 84*x^82 + 31*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 67*x^75 + 36*x^74 + 117*x^73 + 86*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 66*x^68 + 103*x^67 + 124*x^66 + 65*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 25*x^27 + 60*x^26 + 47*x^25 + 82*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 38*x^20 + 125*x^19 + 100*x^18 + 91*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 103*x^11 + 20*x^10 + 113*x^9 + 30*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 90*x^4 + 91*x^3 + 12*x^2 + 45*x + 30, x^95 + 15*x^93 + 126*x^92 + 101*x^91 + 44*x^90 + 3*x^89 + 90*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 62*x^84 + 25*x^83 + 116*x^82 + 31*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 3*x^75 + 68*x^74 + 117*x^73 + 38*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 50*x^68 + 39*x^67 + 92*x^66 + 65*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 89*x^27 + 28*x^26 + 47*x^25 + 66*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 118*x^20 + 61*x^19 + 4*x^18 + 91*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 39*x^11 + 52*x^10 + 113*x^9 + 46*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 10*x^4 + 27*x^3 + 108*x^2 + 45*x + 46, x^95 + 15*x^93 + 114*x^92 + 37*x^91 + 20*x^90 + 3*x^89 + 86*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 114*x^84 + 89*x^83 + 76*x^82 + 31*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 67*x^75 + 124*x^74 + 117*x^73 + 42*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 30*x^68 + 103*x^67 + 100*x^66 + 65*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 25*x^27 + 36*x^26 + 47*x^25 + 46*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 122*x^20 + 125*x^19 + 60*x^18 + 91*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 103*x^11 + 12*x^10 + 113*x^9 + 98*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 6*x^4 + 91*x^3 + 84*x^2 + 45*x + 34, x^95 + 15*x^93 + 2*x^92 + 53*x^91 + 100*x^90 + 115*x^89 + 22*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 98*x^84 + 9*x^83 + 60*x^82 + 111*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 115*x^75 + 108*x^74 + 69*x^73 + 42*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 110*x^68 + 119*x^67 + 52*x^66 + 49*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 105*x^27 + 52*x^26 + 95*x^25 + 110*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 42*x^20 + 109*x^19 + 108*x^18 + 107*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 87*x^11 + 60*x^10 + x^9 + 98*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 22*x^4 + 43*x^3 + 100*x^2 + 93*x + 2, x^95 + 15*x^93 + 118*x^92 + 101*x^91 + 12*x^90 + 35*x^89 + 114*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 86*x^84 + 25*x^83 + 84*x^82 + 127*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 3*x^75 + 100*x^74 + 85*x^73 + 78*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 26*x^68 + 39*x^67 + 124*x^66 + 97*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 89*x^27 + 124*x^26 + 79*x^25 + 58*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 110*x^20 + 61*x^19 + 100*x^18 + 59*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 39*x^11 + 84*x^10 + 81*x^9 + 54*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 82*x^4 + 27*x^3 + 12*x^2 + 77*x + 86, x^95 + 15*x^93 + 86*x^92 + 5*x^91 + 12*x^90 + 3*x^89 + 82*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 54*x^84 + 121*x^83 + 84*x^82 + 31*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 99*x^75 + 100*x^74 + 117*x^73 + 110*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 58*x^68 + 71*x^67 + 124*x^66 + 65*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 121*x^27 + 124*x^26 + 47*x^25 + 26*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 78*x^20 + 29*x^19 + 100*x^18 + 91*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 7*x^11 + 84*x^10 + 113*x^9 + 86*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 114*x^4 + 59*x^3 + 12*x^2 + 45*x + 118, x^95 + 15*x^93 + 54*x^92 + 85*x^91 + 60*x^90 + 115*x^89 + 2*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 118*x^84 + 105*x^83 + 100*x^82 + 111*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 83*x^75 + 116*x^74 + 69*x^73 + 126*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 58*x^68 + 23*x^67 + 44*x^66 + 49*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 9*x^27 + 108*x^26 + 95*x^25 + 10*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 14*x^20 + 77*x^19 + 52*x^18 + 107*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 55*x^11 + 36*x^10 + x^9 + 38*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 114*x^4 + 75*x^3 + 124*x^2 + 93*x + 38, x^95 + 15*x^93 + 14*x^92 + 85*x^91 + 60*x^90 + 19*x^89 + 90*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 46*x^84 + 105*x^83 + 36*x^82 + 79*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 83*x^75 + 116*x^74 + 37*x^73 + 102*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 2*x^68 + 23*x^67 + 108*x^66 + 81*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 9*x^27 + 108*x^26 + 127*x^25 + 66*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 38*x^20 + 77*x^19 + 116*x^18 + 75*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 55*x^11 + 36*x^10 + 97*x^9 + 110*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 26*x^4 + 75*x^3 + 60*x^2 + 125*x + 78, x^95 + 15*x^93 + 10*x^92 + 5*x^91 + 52*x^90 + 67*x^89 + 14*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 42*x^84 + 121*x^83 + 108*x^82 + 95*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 99*x^75 + 92*x^74 + 53*x^73 + 50*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 102*x^68 + 71*x^67 + 68*x^66 + x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 121*x^27 + 68*x^26 + 111*x^25 + 70*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 18*x^20 + 29*x^19 + 92*x^18 + 27*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 7*x^11 + 108*x^10 + 49*x^9 + 74*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 46*x^4 + 59*x^3 + 52*x^2 + 109*x + 42, x^95 + 15*x^93 + 6*x^92 + 117*x^91 + 60*x^90 + 19*x^89 + 82*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 6*x^84 + 73*x^83 + 100*x^82 + 79*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 51*x^75 + 116*x^74 + 37*x^73 + 46*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 42*x^68 + 55*x^67 + 44*x^66 + 81*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 41*x^27 + 108*x^26 + 127*x^25 + 26*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 94*x^20 + 45*x^19 + 52*x^18 + 75*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 23*x^11 + 36*x^10 + 97*x^9 + 22*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 34*x^4 + 107*x^3 + 124*x^2 + 125*x + 86, x^95 + 15*x^93 + 106*x^92 + 21*x^91 + 68*x^90 + 115*x^89 + 94*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 42*x^84 + 41*x^83 + 28*x^82 + 111*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 19*x^75 + 12*x^74 + 69*x^73 + 34*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 38*x^68 + 87*x^67 + 84*x^66 + 49*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 73*x^27 + 20*x^26 + 95*x^25 + 86*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 18*x^20 + 13*x^19 + 76*x^18 + 107*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 119*x^11 + 92*x^10 + x^9 + 122*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 110*x^4 + 11*x^3 + 4*x^2 + 93*x + 122, x^95 + 15*x^93 + 86*x^92 + 117*x^91 + 124*x^90 + 19*x^89 + 34*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 22*x^84 + 73*x^83 + 36*x^82 + 79*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 51*x^75 + 52*x^74 + 37*x^73 + 94*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 26*x^68 + 55*x^67 + 108*x^66 + 81*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 41*x^27 + 44*x^26 + 127*x^25 + 42*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 46*x^20 + 45*x^19 + 116*x^18 + 75*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 23*x^11 + 100*x^10 + 97*x^9 + 6*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 82*x^4 + 107*x^3 + 60*x^2 + 125*x + 6, x^95 + 15*x^93 + 126*x^92 + 85*x^91 + 92*x^90 + 19*x^89 + 106*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 30*x^84 + 105*x^83 + 4*x^82 + 79*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 83*x^75 + 84*x^74 + 37*x^73 + 86*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 18*x^68 + 23*x^67 + 12*x^66 + 81*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 9*x^27 + 12*x^26 + 127*x^25 + 18*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 86*x^20 + 77*x^19 + 84*x^18 + 75*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 55*x^11 + 4*x^10 + 97*x^9 + 30*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 106*x^4 + 75*x^3 + 92*x^2 + 125*x + 126, x^95 + 15*x^93 + 62*x^92 + 85*x^91 + 92*x^90 + 19*x^89 + 42*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 94*x^84 + 105*x^83 + 4*x^82 + 79*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 83*x^75 + 84*x^74 + 37*x^73 + 22*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 82*x^68 + 23*x^67 + 12*x^66 + 81*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 9*x^27 + 12*x^26 + 127*x^25 + 82*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 22*x^20 + 77*x^19 + 84*x^18 + 75*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 55*x^11 + 4*x^10 + 97*x^9 + 94*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 42*x^4 + 75*x^3 + 92*x^2 + 125*x + 62, x^95 + 15*x^93 + 98*x^92 + 37*x^91 + 20*x^90 + 67*x^89 + 70*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 34*x^84 + 89*x^83 + 76*x^82 + 95*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 67*x^75 + 124*x^74 + 53*x^73 + 58*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 110*x^68 + 103*x^67 + 100*x^66 + x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 25*x^27 + 36*x^26 + 111*x^25 + 94*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 106*x^20 + 125*x^19 + 60*x^18 + 27*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 103*x^11 + 12*x^10 + 49*x^9 + 50*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 22*x^4 + 91*x^3 + 84*x^2 + 109*x + 50, x^95 + 15*x^93 + 10*x^92 + 37*x^91 + 116*x^90 + 99*x^89 + 14*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 42*x^84 + 89*x^83 + 44*x^82 + 63*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 67*x^75 + 28*x^74 + 21*x^73 + 50*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 102*x^68 + 103*x^67 + 4*x^66 + 33*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 25*x^27 + 4*x^26 + 15*x^25 + 70*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 18*x^20 + 125*x^19 + 28*x^18 + 123*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 103*x^11 + 44*x^10 + 17*x^9 + 74*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 46*x^4 + 91*x^3 + 116*x^2 + 13*x + 42, x^95 + 15*x^93 + 90*x^92 + 53*x^91 + 68*x^90 + 19*x^89 + 78*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 90*x^84 + 9*x^83 + 28*x^82 + 79*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 115*x^75 + 12*x^74 + 37*x^73 + 50*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 118*x^68 + 119*x^67 + 84*x^66 + 81*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 105*x^27 + 20*x^26 + 127*x^25 + 6*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 2*x^20 + 109*x^19 + 76*x^18 + 75*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 87*x^11 + 92*x^10 + 97*x^9 + 74*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 126*x^4 + 43*x^3 + 4*x^2 + 125*x + 10, x^95 + 15*x^93 + 66*x^92 + 85*x^91 + 68*x^90 + 83*x^89 + 118*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 98*x^84 + 105*x^83 + 92*x^82 + 15*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 83*x^75 + 12*x^74 + 101*x^73 + 74*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 110*x^68 + 23*x^67 + 20*x^66 + 17*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 9*x^27 + 20*x^26 + 63*x^25 + 78*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 42*x^20 + 77*x^19 + 12*x^18 + 11*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 55*x^11 + 92*x^10 + 33*x^9 + 2*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 22*x^4 + 75*x^3 + 68*x^2 + 61*x + 98, x^95 + 15*x^93 + 30*x^92 + 37*x^91 + 108*x^90 + 67*x^89 + 58*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 94*x^84 + 89*x^83 + 52*x^82 + 95*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 67*x^75 + 4*x^74 + 53*x^73 + 70*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 18*x^68 + 103*x^67 + 28*x^66 + x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 25*x^27 + 92*x^26 + 111*x^25 + 34*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 22*x^20 + 125*x^19 + 68*x^18 + 27*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 103*x^11 + 116*x^10 + 49*x^9 + 78*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 106*x^4 + 91*x^3 + 44*x^2 + 109*x + 78, x^95 + 15*x^93 + 126*x^92 + 69*x^91 + 76*x^90 + 99*x^89 + 122*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 126*x^84 + 57*x^83 + 84*x^82 + 63*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 35*x^75 + 36*x^74 + 21*x^73 + 6*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 114*x^68 + 7*x^67 + 124*x^66 + 33*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 57*x^27 + 60*x^26 + 15*x^25 + 98*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 54*x^20 + 93*x^19 + 100*x^18 + 123*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 71*x^11 + 20*x^10 + 17*x^9 + 14*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 74*x^4 + 123*x^3 + 12*x^2 + 13*x + 78, x^95 + 15*x^93 + 106*x^92 + 101*x^91 + 20*x^90 + 99*x^89 + 14*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 74*x^84 + 25*x^83 + 12*x^82 + 63*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 3*x^75 + 124*x^74 + 21*x^73 + 50*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 70*x^68 + 39*x^67 + 36*x^66 + 33*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 89*x^27 + 36*x^26 + 15*x^25 + 70*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 50*x^20 + 61*x^19 + 124*x^18 + 123*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 39*x^11 + 12*x^10 + 17*x^9 + 74*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 14*x^4 + 27*x^3 + 20*x^2 + 13*x + 106, x^95 + 15*x^93 + 126*x^92 + 69*x^91 + 76*x^90 + 35*x^89 + 58*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 126*x^84 + 57*x^83 + 84*x^82 + 127*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 35*x^75 + 36*x^74 + 85*x^73 + 70*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 114*x^68 + 7*x^67 + 124*x^66 + 97*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 57*x^27 + 60*x^26 + 79*x^25 + 34*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 54*x^20 + 93*x^19 + 100*x^18 + 59*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 71*x^11 + 20*x^10 + 81*x^9 + 78*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 74*x^4 + 123*x^3 + 12*x^2 + 77*x + 14, x^95 + 15*x^93 + 26*x^92 + 85*x^91 + 100*x^90 + 115*x^89 + 110*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 90*x^84 + 105*x^83 + 124*x^82 + 111*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 83*x^75 + 108*x^74 + 69*x^73 + 18*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 118*x^68 + 23*x^67 + 116*x^66 + 49*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 9*x^27 + 52*x^26 + 95*x^25 + 38*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 2*x^20 + 77*x^19 + 44*x^18 + 107*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 55*x^11 + 60*x^10 + x^9 + 42*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 126*x^4 + 75*x^3 + 36*x^2 + 93*x + 42, x^95 + 15*x^93 + 22*x^92 + 53*x^91 + 28*x^90 + 83*x^89 + 66*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 22*x^84 + 9*x^83 + 4*x^82 + 15*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 115*x^75 + 20*x^74 + 101*x^73 + 62*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 26*x^68 + 119*x^67 + 12*x^66 + 17*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 105*x^27 + 76*x^26 + 63*x^25 + 74*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 46*x^20 + 109*x^19 + 84*x^18 + 11*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 87*x^11 + 68*x^10 + 33*x^9 + 102*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 82*x^4 + 43*x^3 + 92*x^2 + 61*x + 38, x^95 + 15*x^93 + 82*x^92 + 101*x^91 + 84*x^90 + 3*x^89 + 54*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 82*x^84 + 25*x^83 + 12*x^82 + 31*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 3*x^75 + 60*x^74 + 117*x^73 + 74*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 62*x^68 + 39*x^67 + 36*x^66 + 65*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 89*x^27 + 100*x^26 + 47*x^25 + 14*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 90*x^20 + 61*x^19 + 124*x^18 + 91*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 39*x^11 + 76*x^10 + 113*x^9 + 2*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 38*x^4 + 27*x^3 + 20*x^2 + 45*x + 66, x^95 + 15*x^93 + 106*x^92 + 53*x^91 + 4*x^90 + 19*x^89 + 94*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 42*x^84 + 9*x^83 + 92*x^82 + 79*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 115*x^75 + 76*x^74 + 37*x^73 + 34*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 38*x^68 + 119*x^67 + 20*x^66 + 81*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 105*x^27 + 84*x^26 + 127*x^25 + 86*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 18*x^20 + 109*x^19 + 12*x^18 + 75*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 87*x^11 + 28*x^10 + 97*x^9 + 122*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 110*x^4 + 43*x^3 + 68*x^2 + 125*x + 122, x^95 + 15*x^93 + 30*x^92 + 37*x^91 + 76*x^90 + 67*x^89 + 90*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 30*x^84 + 89*x^83 + 84*x^82 + 95*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 67*x^75 + 36*x^74 + 53*x^73 + 38*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 82*x^68 + 103*x^67 + 124*x^66 + x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 25*x^27 + 60*x^26 + 111*x^25 + 66*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 86*x^20 + 125*x^19 + 100*x^18 + 27*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 103*x^11 + 20*x^10 + 49*x^9 + 46*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 42*x^4 + 91*x^3 + 12*x^2 + 109*x + 110, x^95 + 15*x^93 + 122*x^92 + 53*x^91 + 4*x^90 + 19*x^89 + 46*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 122*x^84 + 9*x^83 + 92*x^82 + 79*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 115*x^75 + 76*x^74 + 37*x^73 + 82*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 86*x^68 + 119*x^67 + 20*x^66 + 81*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 105*x^27 + 84*x^26 + 127*x^25 + 102*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 34*x^20 + 109*x^19 + 12*x^18 + 75*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 87*x^11 + 28*x^10 + 97*x^9 + 106*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 94*x^4 + 43*x^3 + 68*x^2 + 125*x + 42, x^95 + 15*x^93 + 18*x^92 + 117*x^91 + 68*x^90 + 51*x^89 + 6*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 114*x^84 + 73*x^83 + 92*x^82 + 47*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 51*x^75 + 12*x^74 + 5*x^73 + 58*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 94*x^68 + 55*x^67 + 20*x^66 + 113*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 41*x^27 + 20*x^26 + 31*x^25 + 30*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 122*x^20 + 45*x^19 + 12*x^18 + 43*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 23*x^11 + 92*x^10 + 65*x^9 + 50*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 70*x^4 + 107*x^3 + 68*x^2 + 29*x + 82, x^95 + 15*x^93 + 30*x^92 + 117*x^91 + 124*x^90 + 115*x^89 + 106*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 126*x^84 + 73*x^83 + 100*x^82 + 111*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 51*x^75 + 52*x^74 + 69*x^73 + 86*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 50*x^68 + 55*x^67 + 44*x^66 + 49*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 41*x^27 + 44*x^26 + 95*x^25 + 18*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 54*x^20 + 45*x^19 + 52*x^18 + 107*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 23*x^11 + 100*x^10 + x^9 + 30*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 10*x^4 + 107*x^3 + 124*x^2 + 93*x + 62, x^95 + 15*x^93 + 106*x^92 + 85*x^91 + 36*x^90 + 51*x^89 + 126*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 106*x^84 + 105*x^83 + 60*x^82 + 47*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 83*x^75 + 44*x^74 + 5*x^73 + 2*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 102*x^68 + 23*x^67 + 52*x^66 + 113*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 9*x^27 + 116*x^26 + 31*x^25 + 118*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 82*x^20 + 77*x^19 + 108*x^18 + 43*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 55*x^11 + 124*x^10 + 65*x^9 + 90*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 46*x^4 + 75*x^3 + 100*x^2 + 29*x + 26, x^95 + 15*x^93 + 38*x^92 + 101*x^91 + 76*x^90 + 35*x^89 + 34*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 70*x^84 + 25*x^83 + 20*x^82 + 127*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 3*x^75 + 36*x^74 + 85*x^73 + 30*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 42*x^68 + 39*x^67 + 60*x^66 + 97*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 89*x^27 + 60*x^26 + 79*x^25 + 42*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 30*x^20 + 61*x^19 + 36*x^18 + 59*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 39*x^11 + 20*x^10 + 81*x^9 + 70*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 34*x^4 + 27*x^3 + 76*x^2 + 77*x + 38, x^95 + 15*x^93 + 6*x^92 + 85*x^91 + 124*x^90 + 115*x^89 + 82*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 6*x^84 + 105*x^83 + 36*x^82 + 111*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 83*x^75 + 52*x^74 + 69*x^73 + 46*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 42*x^68 + 23*x^67 + 108*x^66 + 49*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 9*x^27 + 44*x^26 + 95*x^25 + 26*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 94*x^20 + 77*x^19 + 116*x^18 + 107*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 55*x^11 + 100*x^10 + x^9 + 22*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 34*x^4 + 75*x^3 + 60*x^2 + 93*x + 86, x^95 + 15*x^93 + 38*x^92 + 5*x^91 + 108*x^90 + 3*x^89 + 2*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 6*x^84 + 121*x^83 + 116*x^82 + 31*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 99*x^75 + 4*x^74 + 117*x^73 + 62*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 106*x^68 + 71*x^67 + 92*x^66 + 65*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 121*x^27 + 92*x^26 + 47*x^25 + 10*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 94*x^20 + 29*x^19 + 4*x^18 + 91*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 7*x^11 + 116*x^10 + 113*x^9 + 102*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 98*x^4 + 59*x^3 + 108*x^2 + 45*x + 6, x^95 + 15*x^93 + 114*x^92 + 53*x^91 + 68*x^90 + 115*x^89 + 102*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 82*x^84 + 9*x^83 + 92*x^82 + 111*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 115*x^75 + 12*x^74 + 69*x^73 + 90*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 126*x^68 + 119*x^67 + 20*x^66 + 49*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 105*x^27 + 20*x^26 + 95*x^25 + 126*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 90*x^20 + 109*x^19 + 12*x^18 + 107*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 87*x^11 + 92*x^10 + x^9 + 82*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 102*x^4 + 43*x^3 + 68*x^2 + 93*x + 114, x^95 + 15*x^93 + 94*x^92 + 21*x^91 + 60*x^90 + 83*x^89 + 106*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 62*x^84 + 41*x^83 + 36*x^82 + 15*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 19*x^75 + 116*x^74 + 101*x^73 + 86*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 114*x^68 + 87*x^67 + 108*x^66 + 17*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 73*x^27 + 108*x^26 + 63*x^25 + 18*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 118*x^20 + 13*x^19 + 116*x^18 + 11*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 119*x^11 + 36*x^10 + 33*x^9 + 30*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 74*x^4 + 11*x^3 + 60*x^2 + 61*x + 62, x^95 + 15*x^93 + 58*x^92 + 21*x^91 + 68*x^90 + 115*x^89 + 110*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 58*x^84 + 41*x^83 + 28*x^82 + 111*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 19*x^75 + 12*x^74 + 69*x^73 + 18*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 22*x^68 + 87*x^67 + 84*x^66 + 49*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 73*x^27 + 20*x^26 + 95*x^25 + 38*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 98*x^20 + 13*x^19 + 76*x^18 + 107*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 119*x^11 + 92*x^10 + x^9 + 42*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 30*x^4 + 11*x^3 + 4*x^2 + 93*x + 106, x^95 + 15*x^93 + 6*x^92 + 21*x^91 + 92*x^90 + 115*x^89 + 50*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 70*x^84 + 41*x^83 + 68*x^82 + 111*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 19*x^75 + 84*x^74 + 69*x^73 + 78*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 106*x^68 + 87*x^67 + 76*x^66 + 49*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 73*x^27 + 12*x^26 + 95*x^25 + 122*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 30*x^20 + 13*x^19 + 20*x^18 + 107*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 119*x^11 + 4*x^10 + x^9 + 54*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 98*x^4 + 11*x^3 + 28*x^2 + 93*x + 54, x^95 + 15*x^93 + 34*x^92 + 53*x^91 + 36*x^90 + 115*x^89 + 118*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 2*x^84 + 9*x^83 + 124*x^82 + 111*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 115*x^75 + 44*x^74 + 69*x^73 + 74*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 78*x^68 + 119*x^67 + 116*x^66 + 49*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 105*x^27 + 116*x^26 + 95*x^25 + 78*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 74*x^20 + 109*x^19 + 44*x^18 + 107*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 87*x^11 + 124*x^10 + x^9 + 2*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 118*x^4 + 43*x^3 + 36*x^2 + 93*x + 34, x^95 + 15*x^93 + 82*x^92 + 5*x^91 + 20*x^90 + 35*x^89 + 54*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 82*x^84 + 121*x^83 + 76*x^82 + 127*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 99*x^75 + 124*x^74 + 85*x^73 + 74*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 62*x^68 + 71*x^67 + 100*x^66 + 97*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 121*x^27 + 36*x^26 + 79*x^25 + 14*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 90*x^20 + 29*x^19 + 60*x^18 + 59*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 7*x^11 + 12*x^10 + 81*x^9 + 2*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 38*x^4 + 59*x^3 + 84*x^2 + 77*x + 66, x^95 + 15*x^93 + 54*x^92 + 5*x^91 + 76*x^90 + 67*x^89 + 50*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 22*x^84 + 121*x^83 + 20*x^82 + 95*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 99*x^75 + 36*x^74 + 53*x^73 + 14*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 90*x^68 + 71*x^67 + 60*x^66 + x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 121*x^27 + 60*x^26 + 111*x^25 + 122*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 46*x^20 + 29*x^19 + 36*x^18 + 27*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 7*x^11 + 20*x^10 + 49*x^9 + 118*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 18*x^4 + 59*x^3 + 76*x^2 + 109*x + 22, x^95 + 15*x^93 + 46*x^92 + 69*x^91 + 44*x^90 + 99*x^89 + 10*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 46*x^84 + 57*x^83 + 116*x^82 + 63*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 35*x^75 + 68*x^74 + 21*x^73 + 118*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 66*x^68 + 7*x^67 + 92*x^66 + 33*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 57*x^27 + 28*x^26 + 15*x^25 + 50*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 38*x^20 + 93*x^19 + 4*x^18 + 123*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 71*x^11 + 52*x^10 + 17*x^9 + 62*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 90*x^4 + 123*x^3 + 108*x^2 + 13*x + 126, x^95 + 15*x^93 + 62*x^92 + 85*x^91 + 28*x^90 + 19*x^89 + 106*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 94*x^84 + 105*x^83 + 68*x^82 + 79*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 83*x^75 + 20*x^74 + 37*x^73 + 86*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 82*x^68 + 23*x^67 + 76*x^66 + 81*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 9*x^27 + 76*x^26 + 127*x^25 + 18*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 22*x^20 + 77*x^19 + 20*x^18 + 75*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 55*x^11 + 68*x^10 + 97*x^9 + 30*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 42*x^4 + 75*x^3 + 28*x^2 + 125*x + 126, x^95 + 15*x^93 + 38*x^92 + 53*x^91 + 28*x^90 + 83*x^89 + 18*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 102*x^84 + 9*x^83 + 4*x^82 + 15*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 115*x^75 + 20*x^74 + 101*x^73 + 110*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 74*x^68 + 119*x^67 + 12*x^66 + 17*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 105*x^27 + 76*x^26 + 63*x^25 + 90*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 62*x^20 + 109*x^19 + 84*x^18 + 11*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 87*x^11 + 68*x^10 + 33*x^9 + 86*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 66*x^4 + 43*x^3 + 92*x^2 + 61*x + 86, x^95 + 15*x^93 + 42*x^92 + 37*x^91 + 116*x^90 + 35*x^89 + 110*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 74*x^84 + 89*x^83 + 44*x^82 + 127*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 67*x^75 + 28*x^74 + 85*x^73 + 82*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 70*x^68 + 103*x^67 + 4*x^66 + 97*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 25*x^27 + 4*x^26 + 79*x^25 + 38*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 50*x^20 + 125*x^19 + 28*x^18 + 59*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 103*x^11 + 44*x^10 + 81*x^9 + 106*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 14*x^4 + 91*x^3 + 116*x^2 + 77*x + 74, x^95 + 15*x^93 + 114*x^92 + 5*x^91 + 84*x^90 + 99*x^89 + 86*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 114*x^84 + 121*x^83 + 12*x^82 + 63*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 99*x^75 + 60*x^74 + 21*x^73 + 42*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 30*x^68 + 71*x^67 + 36*x^66 + 33*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 121*x^27 + 100*x^26 + 15*x^25 + 46*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 122*x^20 + 29*x^19 + 124*x^18 + 123*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 7*x^11 + 76*x^10 + 17*x^9 + 98*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 6*x^4 + 59*x^3 + 20*x^2 + 13*x + 34, x^95 + 15*x^93 + 38*x^92 + 53*x^91 + 28*x^90 + 19*x^89 + 82*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 102*x^84 + 9*x^83 + 4*x^82 + 79*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 115*x^75 + 20*x^74 + 37*x^73 + 46*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 74*x^68 + 119*x^67 + 12*x^66 + 81*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 105*x^27 + 76*x^26 + 127*x^25 + 26*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 62*x^20 + 109*x^19 + 84*x^18 + 75*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 87*x^11 + 68*x^10 + 97*x^9 + 22*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 66*x^4 + 43*x^3 + 92*x^2 + 125*x + 22, x^95 + 15*x^93 + 122*x^92 + 117*x^91 + 68*x^90 + 83*x^89 + 110*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 122*x^84 + 73*x^83 + 28*x^82 + 15*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 51*x^75 + 12*x^74 + 101*x^73 + 18*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 86*x^68 + 55*x^67 + 84*x^66 + 17*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 41*x^27 + 20*x^26 + 63*x^25 + 38*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 34*x^20 + 45*x^19 + 76*x^18 + 11*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 23*x^11 + 92*x^10 + 33*x^9 + 42*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 94*x^4 + 107*x^3 + 4*x^2 + 61*x + 106, x^95 + 15*x^93 + 26*x^92 + 101*x^91 + 52*x^90 + 35*x^89 + 30*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 122*x^84 + 25*x^83 + 108*x^82 + 127*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 3*x^75 + 92*x^74 + 85*x^73 + 34*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 22*x^68 + 39*x^67 + 68*x^66 + 97*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 89*x^27 + 68*x^26 + 79*x^25 + 22*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 34*x^20 + 61*x^19 + 92*x^18 + 59*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 39*x^11 + 108*x^10 + 81*x^9 + 122*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 30*x^4 + 27*x^3 + 52*x^2 + 77*x + 26, x^95 + 15*x^93 + 86*x^92 + 69*x^91 + 12*x^90 + 67*x^89 + 82*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 54*x^84 + 57*x^83 + 84*x^82 + 95*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 35*x^75 + 100*x^74 + 53*x^73 + 110*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 58*x^68 + 7*x^67 + 124*x^66 + x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 57*x^27 + 124*x^26 + 111*x^25 + 26*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 78*x^20 + 93*x^19 + 100*x^18 + 27*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 71*x^11 + 84*x^10 + 49*x^9 + 86*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 114*x^4 + 123*x^3 + 12*x^2 + 109*x + 118, x^95 + 15*x^93 + 126*x^92 + 117*x^91 + 28*x^90 + 115*x^89 + 42*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 30*x^84 + 73*x^83 + 68*x^82 + 111*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 51*x^75 + 20*x^74 + 69*x^73 + 22*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 18*x^68 + 55*x^67 + 76*x^66 + 49*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 41*x^27 + 76*x^26 + 95*x^25 + 82*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 86*x^20 + 45*x^19 + 20*x^18 + 107*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 23*x^11 + 68*x^10 + x^9 + 94*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 106*x^4 + 107*x^3 + 28*x^2 + 93*x + 62, x^95 + 15*x^93 + 42*x^92 + 5*x^91 + 84*x^90 + 67*x^89 + 14*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 10*x^84 + 121*x^83 + 76*x^82 + 95*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 99*x^75 + 60*x^74 + 53*x^73 + 50*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 6*x^68 + 71*x^67 + 100*x^66 + x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 121*x^27 + 100*x^26 + 111*x^25 + 70*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 114*x^20 + 29*x^19 + 60*x^18 + 27*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 7*x^11 + 76*x^10 + 49*x^9 + 74*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 78*x^4 + 59*x^3 + 84*x^2 + 109*x + 106, x^95 + 15*x^93 + 126*x^92 + 101*x^91 + 44*x^90 + 67*x^89 + 26*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 62*x^84 + 25*x^83 + 116*x^82 + 95*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 3*x^75 + 68*x^74 + 53*x^73 + 102*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 50*x^68 + 39*x^67 + 92*x^66 + x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 89*x^27 + 28*x^26 + 111*x^25 + 2*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 118*x^20 + 61*x^19 + 4*x^18 + 27*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 39*x^11 + 52*x^10 + 49*x^9 + 110*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 10*x^4 + 27*x^3 + 108*x^2 + 109*x + 110, x^95 + 15*x^93 + 58*x^92 + 53*x^91 + 4*x^90 + 83*x^89 + 46*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 58*x^84 + 9*x^83 + 92*x^82 + 15*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 115*x^75 + 76*x^74 + 101*x^73 + 82*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 22*x^68 + 119*x^67 + 20*x^66 + 17*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 105*x^27 + 84*x^26 + 63*x^25 + 102*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 98*x^20 + 109*x^19 + 12*x^18 + 11*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 87*x^11 + 28*x^10 + 33*x^9 + 106*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 30*x^4 + 43*x^3 + 68*x^2 + 61*x + 42, x^95 + 15*x^93 + 46*x^92 + 53*x^91 + 124*x^90 + 115*x^89 + 122*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 78*x^84 + 9*x^83 + 100*x^82 + 111*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 115*x^75 + 52*x^74 + 69*x^73 + 70*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 98*x^68 + 119*x^67 + 44*x^66 + 49*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 105*x^27 + 44*x^26 + 95*x^25 + 98*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 70*x^20 + 109*x^19 + 52*x^18 + 107*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 87*x^11 + 100*x^10 + x^9 + 78*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 122*x^4 + 43*x^3 + 124*x^2 + 93*x + 46, x^95 + 15*x^93 + 70*x^92 + 5*x^91 + 44*x^90 + 3*x^89 + 98*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 38*x^84 + 121*x^83 + 52*x^82 + 31*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 99*x^75 + 68*x^74 + 117*x^73 + 94*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 74*x^68 + 71*x^67 + 28*x^66 + 65*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 121*x^27 + 28*x^26 + 47*x^25 + 106*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 126*x^20 + 29*x^19 + 68*x^18 + 91*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 7*x^11 + 52*x^10 + 113*x^9 + 6*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 66*x^4 + 59*x^3 + 44*x^2 + 45*x + 38, x^95 + 15*x^93 + 22*x^92 + 37*x^91 + 76*x^90 + 99*x^89 + 82*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 118*x^84 + 89*x^83 + 20*x^82 + 63*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 67*x^75 + 36*x^74 + 21*x^73 + 110*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 122*x^68 + 103*x^67 + 60*x^66 + 33*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 25*x^27 + 60*x^26 + 15*x^25 + 26*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 14*x^20 + 125*x^19 + 36*x^18 + 123*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 103*x^11 + 20*x^10 + 17*x^9 + 86*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 50*x^4 + 91*x^3 + 76*x^2 + 13*x + 118, x^95 + 15*x^93 + 74*x^92 + 37*x^91 + 20*x^90 + 99*x^89 + 46*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 42*x^84 + 89*x^83 + 12*x^82 + 63*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 67*x^75 + 124*x^74 + 21*x^73 + 18*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 102*x^68 + 103*x^67 + 36*x^66 + 33*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 25*x^27 + 36*x^26 + 15*x^25 + 102*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 18*x^20 + 125*x^19 + 124*x^18 + 123*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 103*x^11 + 12*x^10 + 17*x^9 + 42*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 46*x^4 + 91*x^3 + 20*x^2 + 13*x + 74, x^95 + 15*x^93 + 74*x^92 + 69*x^91 + 52*x^90 + 3*x^89 + 78*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 106*x^84 + 57*x^83 + 108*x^82 + 31*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 35*x^75 + 92*x^74 + 117*x^73 + 114*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 38*x^68 + 7*x^67 + 68*x^66 + 65*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 57*x^27 + 68*x^26 + 47*x^25 + 6*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 82*x^20 + 93*x^19 + 92*x^18 + 91*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 71*x^11 + 108*x^10 + 113*x^9 + 10*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 110*x^4 + 123*x^3 + 52*x^2 + 45*x + 106, x^95 + 15*x^93 + 82*x^92 + 37*x^91 + 84*x^90 + 3*x^89 + 118*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 82*x^84 + 89*x^83 + 12*x^82 + 31*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 67*x^75 + 60*x^74 + 117*x^73 + 10*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 62*x^68 + 103*x^67 + 36*x^66 + 65*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 25*x^27 + 100*x^26 + 47*x^25 + 78*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 90*x^20 + 125*x^19 + 124*x^18 + 91*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 103*x^11 + 76*x^10 + 113*x^9 + 66*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 38*x^4 + 91*x^3 + 20*x^2 + 45*x + 2, x^95 + 15*x^93 + 58*x^92 + 101*x^91 + 52*x^90 + 99*x^89 + 126*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 26*x^84 + 25*x^83 + 108*x^82 + 63*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 3*x^75 + 92*x^74 + 21*x^73 + 66*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 118*x^68 + 39*x^67 + 68*x^66 + 33*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 89*x^27 + 68*x^26 + 15*x^25 + 118*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 66*x^20 + 61*x^19 + 92*x^18 + 123*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 39*x^11 + 108*x^10 + 17*x^9 + 26*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 126*x^4 + 27*x^3 + 52*x^2 + 13*x + 58, x^95 + 15*x^93 + 26*x^92 + 101*x^91 + 52*x^90 + 99*x^89 + 94*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 122*x^84 + 25*x^83 + 108*x^82 + 63*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 3*x^75 + 92*x^74 + 21*x^73 + 98*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 22*x^68 + 39*x^67 + 68*x^66 + 33*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 89*x^27 + 68*x^26 + 15*x^25 + 86*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 34*x^20 + 61*x^19 + 92*x^18 + 123*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 39*x^11 + 108*x^10 + 17*x^9 + 58*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 30*x^4 + 27*x^3 + 52*x^2 + 13*x + 90, x^95 + 15*x^93 + 106*x^92 + 101*x^91 + 20*x^90 + 35*x^89 + 78*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 74*x^84 + 25*x^83 + 12*x^82 + 127*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 3*x^75 + 124*x^74 + 85*x^73 + 114*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 70*x^68 + 39*x^67 + 36*x^66 + 97*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 89*x^27 + 36*x^26 + 79*x^25 + 6*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 50*x^20 + 61*x^19 + 124*x^18 + 59*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 39*x^11 + 12*x^10 + 81*x^9 + 10*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 14*x^4 + 27*x^3 + 20*x^2 + 77*x + 42, x^95 + 15*x^93 + 118*x^92 + 69*x^91 + 44*x^90 + 3*x^89 + 18*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 22*x^84 + 57*x^83 + 52*x^82 + 31*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 35*x^75 + 68*x^74 + 117*x^73 + 46*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 90*x^68 + 7*x^67 + 28*x^66 + 65*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 57*x^27 + 28*x^26 + 47*x^25 + 90*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 46*x^20 + 93*x^19 + 68*x^18 + 91*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 71*x^11 + 52*x^10 + 113*x^9 + 22*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 18*x^4 + 123*x^3 + 44*x^2 + 45*x + 118, x^95 + 15*x^93 + 114*x^92 + 37*x^91 + 20*x^90 + 67*x^89 + 22*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 114*x^84 + 89*x^83 + 76*x^82 + 95*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 67*x^75 + 124*x^74 + 53*x^73 + 106*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 30*x^68 + 103*x^67 + 100*x^66 + x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 25*x^27 + 36*x^26 + 111*x^25 + 110*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 122*x^20 + 125*x^19 + 60*x^18 + 27*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 103*x^11 + 12*x^10 + 49*x^9 + 34*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 6*x^4 + 91*x^3 + 84*x^2 + 109*x + 98, x^95 + 15*x^93 + 66*x^92 + 117*x^91 + 68*x^90 + 51*x^89 + 118*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 98*x^84 + 73*x^83 + 92*x^82 + 47*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 51*x^75 + 12*x^74 + 5*x^73 + 74*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 110*x^68 + 55*x^67 + 20*x^66 + 113*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 41*x^27 + 20*x^26 + 31*x^25 + 78*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 42*x^20 + 45*x^19 + 12*x^18 + 43*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 23*x^11 + 92*x^10 + 65*x^9 + 2*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 22*x^4 + 107*x^3 + 68*x^2 + 29*x + 98, x^95 + 15*x^93 + 118*x^92 + 21*x^91 + 124*x^90 + 115*x^89 + 66*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 54*x^84 + 41*x^83 + 36*x^82 + 111*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 19*x^75 + 52*x^74 + 69*x^73 + 62*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 122*x^68 + 87*x^67 + 108*x^66 + 49*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 73*x^27 + 44*x^26 + 95*x^25 + 74*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 78*x^20 + 13*x^19 + 116*x^18 + 107*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 119*x^11 + 100*x^10 + x^9 + 102*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 50*x^4 + 11*x^3 + 60*x^2 + 93*x + 102, x^95 + 15*x^93 + 118*x^92 + 117*x^91 + 28*x^90 + 83*x^89 + 98*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 118*x^84 + 73*x^83 + 4*x^82 + 15*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 51*x^75 + 20*x^74 + 101*x^73 + 30*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 58*x^68 + 55*x^67 + 12*x^66 + 17*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 41*x^27 + 76*x^26 + 63*x^25 + 106*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 14*x^20 + 45*x^19 + 84*x^18 + 11*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 23*x^11 + 68*x^10 + 33*x^9 + 70*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 114*x^4 + 107*x^3 + 92*x^2 + 61*x + 6, x^95 + 15*x^93 + 46*x^92 + 85*x^91 + 92*x^90 + 83*x^89 + 26*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 14*x^84 + 105*x^83 + 4*x^82 + 15*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 83*x^75 + 84*x^74 + 101*x^73 + 38*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 34*x^68 + 23*x^67 + 12*x^66 + 17*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 9*x^27 + 12*x^26 + 63*x^25 + 2*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 6*x^20 + 77*x^19 + 84*x^18 + 11*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 55*x^11 + 4*x^10 + 33*x^9 + 46*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 58*x^4 + 75*x^3 + 92*x^2 + 61*x + 78, x^95 + 15*x^93 + 42*x^92 + 85*x^91 + 100*x^90 + 115*x^89 + 62*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 42*x^84 + 105*x^83 + 124*x^82 + 111*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 83*x^75 + 108*x^74 + 69*x^73 + 66*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 38*x^68 + 23*x^67 + 116*x^66 + 49*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 9*x^27 + 52*x^26 + 95*x^25 + 54*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 18*x^20 + 77*x^19 + 44*x^18 + 107*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 55*x^11 + 60*x^10 + x^9 + 26*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 110*x^4 + 75*x^3 + 36*x^2 + 93*x + 90, x^95 + 15*x^93 + 106*x^92 + 37*x^91 + 52*x^90 + 35*x^89 + 110*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 10*x^84 + 89*x^83 + 108*x^82 + 127*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 67*x^75 + 92*x^74 + 85*x^73 + 82*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 6*x^68 + 103*x^67 + 68*x^66 + 97*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 25*x^27 + 68*x^26 + 79*x^25 + 38*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 114*x^20 + 125*x^19 + 92*x^18 + 59*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 103*x^11 + 108*x^10 + 81*x^9 + 106*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 78*x^4 + 91*x^3 + 52*x^2 + 77*x + 74, x^95 + 15*x^93 + 38*x^92 + 69*x^91 + 108*x^90 + 67*x^89 + 2*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 6*x^84 + 57*x^83 + 116*x^82 + 95*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 35*x^75 + 4*x^74 + 53*x^73 + 62*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 106*x^68 + 7*x^67 + 92*x^66 + x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 57*x^27 + 92*x^26 + 111*x^25 + 10*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 94*x^20 + 93*x^19 + 4*x^18 + 27*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 71*x^11 + 116*x^10 + 49*x^9 + 102*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 98*x^4 + 123*x^3 + 108*x^2 + 109*x + 6, x^95 + 15*x^93 + 94*x^92 + 5*x^91 + 108*x^90 + 99*x^89 + 122*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 30*x^84 + 121*x^83 + 52*x^82 + 63*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 99*x^75 + 4*x^74 + 21*x^73 + 6*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 82*x^68 + 71*x^67 + 28*x^66 + 33*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 121*x^27 + 92*x^26 + 15*x^25 + 98*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 86*x^20 + 29*x^19 + 68*x^18 + 123*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 7*x^11 + 116*x^10 + 17*x^9 + 14*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 42*x^4 + 59*x^3 + 44*x^2 + 13*x + 14, x^95 + 15*x^93 + 22*x^92 + 117*x^91 + 60*x^90 + 83*x^89 + 98*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 86*x^84 + 73*x^83 + 100*x^82 + 15*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 51*x^75 + 116*x^74 + 101*x^73 + 30*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 90*x^68 + 55*x^67 + 44*x^66 + 17*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 41*x^27 + 108*x^26 + 63*x^25 + 106*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 110*x^20 + 45*x^19 + 52*x^18 + 11*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 23*x^11 + 36*x^10 + 33*x^9 + 70*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 18*x^4 + 107*x^3 + 124*x^2 + 61*x + 70, x^95 + 15*x^93 + 110*x^92 + 85*x^91 + 28*x^90 + 83*x^89 + 26*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 78*x^84 + 105*x^83 + 68*x^82 + 15*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 83*x^75 + 20*x^74 + 101*x^73 + 38*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 98*x^68 + 23*x^67 + 76*x^66 + 17*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 9*x^27 + 76*x^26 + 63*x^25 + 2*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 70*x^20 + 77*x^19 + 20*x^18 + 11*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 55*x^11 + 68*x^10 + 33*x^9 + 46*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 122*x^4 + 75*x^3 + 28*x^2 + 61*x + 78, x^95 + 15*x^93 + 102*x^92 + 53*x^91 + 60*x^90 + 19*x^89 + 114*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 102*x^84 + 9*x^83 + 100*x^82 + 79*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 115*x^75 + 116*x^74 + 37*x^73 + 14*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 74*x^68 + 119*x^67 + 44*x^66 + 81*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 105*x^27 + 108*x^26 + 127*x^25 + 58*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 62*x^20 + 109*x^19 + 52*x^18 + 75*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 87*x^11 + 36*x^10 + 97*x^9 + 118*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 66*x^4 + 43*x^3 + 124*x^2 + 125*x + 54, x^95 + 15*x^93 + 30*x^92 + 21*x^91 + 92*x^90 + 19*x^89 + 74*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 62*x^84 + 41*x^83 + 4*x^82 + 79*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 19*x^75 + 84*x^74 + 37*x^73 + 118*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 114*x^68 + 87*x^67 + 12*x^66 + 81*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 73*x^27 + 12*x^26 + 127*x^25 + 114*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 118*x^20 + 13*x^19 + 84*x^18 + 75*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 119*x^11 + 4*x^10 + 97*x^9 + 62*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 74*x^4 + 11*x^3 + 92*x^2 + 125*x + 30, x^95 + 15*x^93 + 78*x^92 + 5*x^91 + 12*x^90 + 99*x^89 + 10*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 14*x^84 + 121*x^83 + 20*x^82 + 63*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 99*x^75 + 100*x^74 + 21*x^73 + 118*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 98*x^68 + 71*x^67 + 60*x^66 + 33*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 121*x^27 + 124*x^26 + 15*x^25 + 50*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 6*x^20 + 29*x^19 + 36*x^18 + 123*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 7*x^11 + 84*x^10 + 17*x^9 + 62*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 122*x^4 + 59*x^3 + 76*x^2 + 13*x + 62, x^95 + 15*x^93 + 10*x^92 + 5*x^91 + 116*x^90 + 67*x^89 + 78*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 42*x^84 + 121*x^83 + 44*x^82 + 95*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 99*x^75 + 28*x^74 + 53*x^73 + 114*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 102*x^68 + 71*x^67 + 4*x^66 + x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 121*x^27 + 4*x^26 + 111*x^25 + 6*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 18*x^20 + 29*x^19 + 28*x^18 + 27*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 7*x^11 + 44*x^10 + 49*x^9 + 10*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 46*x^4 + 59*x^3 + 116*x^2 + 109*x + 106, x^95 + 15*x^93 + 66*x^92 + 5*x^91 + 52*x^90 + 35*x^89 + 70*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 66*x^84 + 121*x^83 + 44*x^82 + 127*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 99*x^75 + 92*x^74 + 85*x^73 + 58*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 78*x^68 + 71*x^67 + 4*x^66 + 97*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 121*x^27 + 68*x^26 + 79*x^25 + 94*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 10*x^20 + 29*x^19 + 28*x^18 + 59*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 7*x^11 + 108*x^10 + 81*x^9 + 50*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 118*x^4 + 59*x^3 + 116*x^2 + 77*x + 114, x^95 + 15*x^93 + 110*x^92 + 5*x^91 + 76*x^90 + 99*x^89 + 106*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 46*x^84 + 121*x^83 + 84*x^82 + 63*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 99*x^75 + 36*x^74 + 21*x^73 + 22*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 66*x^68 + 71*x^67 + 124*x^66 + 33*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 121*x^27 + 60*x^26 + 15*x^25 + 18*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 38*x^20 + 29*x^19 + 100*x^18 + 123*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 7*x^11 + 20*x^10 + 17*x^9 + 94*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 90*x^4 + 59*x^3 + 12*x^2 + 13*x + 94, x^95 + 15*x^93 + 126*x^92 + 53*x^91 + 60*x^90 + 51*x^89 + 10*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 94*x^84 + 9*x^83 + 36*x^82 + 47*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 115*x^75 + 116*x^74 + 5*x^73 + 54*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 82*x^68 + 119*x^67 + 108*x^66 + 113*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 105*x^27 + 108*x^26 + 31*x^25 + 50*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 22*x^20 + 109*x^19 + 116*x^18 + 43*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 87*x^11 + 36*x^10 + 65*x^9 + 126*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 42*x^4 + 43*x^3 + 60*x^2 + 29*x + 30, x^95 + 15*x^93 + 62*x^92 + 5*x^91 + 76*x^90 + 99*x^89 + 122*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 62*x^84 + 121*x^83 + 84*x^82 + 63*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 99*x^75 + 36*x^74 + 21*x^73 + 6*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 50*x^68 + 71*x^67 + 124*x^66 + 33*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 121*x^27 + 60*x^26 + 15*x^25 + 98*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 118*x^20 + 29*x^19 + 100*x^18 + 123*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 7*x^11 + 20*x^10 + 17*x^9 + 14*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 10*x^4 + 59*x^3 + 12*x^2 + 13*x + 78, x^95 + 15*x^93 + 98*x^92 + 21*x^91 + 100*x^90 + 83*x^89 + 54*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 66*x^84 + 41*x^83 + 60*x^82 + 15*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 19*x^75 + 108*x^74 + 101*x^73 + 10*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 14*x^68 + 87*x^67 + 52*x^66 + 17*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 73*x^27 + 52*x^26 + 63*x^25 + 14*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 10*x^20 + 13*x^19 + 108*x^18 + 11*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 119*x^11 + 60*x^10 + 33*x^9 + 66*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 54*x^4 + 11*x^3 + 100*x^2 + 61*x + 98, x^95 + 15*x^93 + 6*x^92 + 37*x^91 + 44*x^90 + 35*x^89 + 98*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 102*x^84 + 89*x^83 + 52*x^82 + 127*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 67*x^75 + 68*x^74 + 85*x^73 + 94*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 10*x^68 + 103*x^67 + 28*x^66 + 97*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 25*x^27 + 28*x^26 + 79*x^25 + 106*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 62*x^20 + 125*x^19 + 68*x^18 + 59*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 103*x^11 + 52*x^10 + 81*x^9 + 6*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 2*x^4 + 91*x^3 + 44*x^2 + 77*x + 38, x^95 + 15*x^93 + 18*x^92 + 117*x^91 + 100*x^90 + 51*x^89 + 102*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 50*x^84 + 73*x^83 + 60*x^82 + 47*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 51*x^75 + 108*x^74 + 5*x^73 + 90*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 30*x^68 + 55*x^67 + 52*x^66 + 113*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 41*x^27 + 52*x^26 + 31*x^25 + 126*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 58*x^20 + 45*x^19 + 108*x^18 + 43*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 23*x^11 + 60*x^10 + 65*x^9 + 82*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 6*x^4 + 107*x^3 + 100*x^2 + 29*x + 50, x^95 + 15*x^93 + 42*x^92 + 5*x^91 + 20*x^90 + 67*x^89 + 78*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 10*x^84 + 121*x^83 + 12*x^82 + 95*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 99*x^75 + 124*x^74 + 53*x^73 + 114*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 6*x^68 + 71*x^67 + 36*x^66 + x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 121*x^27 + 36*x^26 + 111*x^25 + 6*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 114*x^20 + 29*x^19 + 124*x^18 + 27*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 7*x^11 + 12*x^10 + 49*x^9 + 10*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 78*x^4 + 59*x^3 + 20*x^2 + 109*x + 42, x^95 + 15*x^93 + 34*x^92 + 53*x^91 + 4*x^90 + 115*x^89 + 22*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 66*x^84 + 9*x^83 + 28*x^82 + 111*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 115*x^75 + 76*x^74 + 69*x^73 + 42*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 14*x^68 + 119*x^67 + 84*x^66 + 49*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 105*x^27 + 84*x^26 + 95*x^25 + 110*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 10*x^20 + 109*x^19 + 76*x^18 + 107*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 87*x^11 + 28*x^10 + x^9 + 98*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 54*x^4 + 43*x^3 + 4*x^2 + 93*x + 66, x^95 + 15*x^93 + 46*x^92 + 21*x^91 + 92*x^90 + 19*x^89 + 26*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 14*x^84 + 41*x^83 + 4*x^82 + 79*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 19*x^75 + 84*x^74 + 37*x^73 + 38*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 34*x^68 + 87*x^67 + 12*x^66 + 81*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 73*x^27 + 12*x^26 + 127*x^25 + 2*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 6*x^20 + 13*x^19 + 84*x^18 + 75*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 119*x^11 + 4*x^10 + 97*x^9 + 46*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 58*x^4 + 11*x^3 + 92*x^2 + 125*x + 78, x^95 + 15*x^93 + 86*x^92 + 5*x^91 + 44*x^90 + 3*x^89 + 50*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 118*x^84 + 121*x^83 + 52*x^82 + 31*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 99*x^75 + 68*x^74 + 117*x^73 + 14*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 122*x^68 + 71*x^67 + 28*x^66 + 65*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 121*x^27 + 28*x^26 + 47*x^25 + 122*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 14*x^20 + 29*x^19 + 68*x^18 + 91*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 7*x^11 + 52*x^10 + 113*x^9 + 118*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 50*x^4 + 59*x^3 + 44*x^2 + 45*x + 86, x^95 + 15*x^93 + 102*x^92 + 117*x^91 + 92*x^90 + 19*x^89 + 18*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 38*x^84 + 73*x^83 + 68*x^82 + 79*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 51*x^75 + 84*x^74 + 37*x^73 + 110*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 10*x^68 + 55*x^67 + 76*x^66 + 81*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 41*x^27 + 12*x^26 + 127*x^25 + 90*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 126*x^20 + 45*x^19 + 20*x^18 + 75*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 23*x^11 + 4*x^10 + 97*x^9 + 86*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 2*x^4 + 107*x^3 + 28*x^2 + 125*x + 86, x^95 + 15*x^93 + 22*x^92 + 5*x^91 + 108*x^90 + 3*x^89 + 50*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 54*x^84 + 121*x^83 + 116*x^82 + 31*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 99*x^75 + 4*x^74 + 117*x^73 + 14*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 58*x^68 + 71*x^67 + 92*x^66 + 65*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 121*x^27 + 92*x^26 + 47*x^25 + 122*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 78*x^20 + 29*x^19 + 4*x^18 + 91*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 7*x^11 + 116*x^10 + 113*x^9 + 118*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 114*x^4 + 59*x^3 + 108*x^2 + 45*x + 86, x^95 + 15*x^93 + 126*x^92 + 69*x^91 + 44*x^90 + 35*x^89 + 90*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 62*x^84 + 57*x^83 + 116*x^82 + 127*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 35*x^75 + 68*x^74 + 85*x^73 + 38*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 50*x^68 + 7*x^67 + 92*x^66 + 97*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 57*x^27 + 28*x^26 + 79*x^25 + 66*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 118*x^20 + 93*x^19 + 4*x^18 + 59*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 71*x^11 + 52*x^10 + 81*x^9 + 46*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 10*x^4 + 123*x^3 + 108*x^2 + 77*x + 46, x^95 + 15*x^93 + 82*x^92 + 5*x^91 + 116*x^90 + 99*x^89 + 22*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 18*x^84 + 121*x^83 + 108*x^82 + 63*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 99*x^75 + 28*x^74 + 21*x^73 + 106*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 126*x^68 + 71*x^67 + 68*x^66 + 33*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 121*x^27 + 4*x^26 + 15*x^25 + 110*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 26*x^20 + 29*x^19 + 92*x^18 + 123*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 7*x^11 + 44*x^10 + 17*x^9 + 34*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 102*x^4 + 59*x^3 + 52*x^2 + 13*x + 34, x^95 + 15*x^93 + 94*x^92 + 21*x^91 + 28*x^90 + 83*x^89 + 10*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 126*x^84 + 41*x^83 + 68*x^82 + 15*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 19*x^75 + 20*x^74 + 101*x^73 + 54*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 50*x^68 + 87*x^67 + 76*x^66 + 17*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 73*x^27 + 76*x^26 + 63*x^25 + 50*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 54*x^20 + 13*x^19 + 20*x^18 + 11*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 119*x^11 + 68*x^10 + 33*x^9 + 126*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 10*x^4 + 11*x^3 + 28*x^2 + 61*x + 94, x^95 + 15*x^93 + 110*x^92 + 117*x^91 + 60*x^90 + 51*x^89 + 122*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 14*x^84 + 73*x^83 + 36*x^82 + 47*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 51*x^75 + 116*x^74 + 5*x^73 + 70*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 34*x^68 + 55*x^67 + 108*x^66 + 113*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 41*x^27 + 108*x^26 + 31*x^25 + 98*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 6*x^20 + 45*x^19 + 116*x^18 + 43*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 23*x^11 + 36*x^10 + 65*x^9 + 78*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 58*x^4 + 107*x^3 + 60*x^2 + 29*x + 46, x^95 + 15*x^93 + 62*x^92 + 69*x^91 + 108*x^90 + 35*x^89 + 90*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 126*x^84 + 57*x^83 + 52*x^82 + 127*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 35*x^75 + 4*x^74 + 85*x^73 + 38*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 114*x^68 + 7*x^67 + 28*x^66 + 97*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 57*x^27 + 92*x^26 + 79*x^25 + 66*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 54*x^20 + 93*x^19 + 68*x^18 + 59*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 71*x^11 + 116*x^10 + 81*x^9 + 46*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 74*x^4 + 123*x^3 + 44*x^2 + 77*x + 46, x^95 + 15*x^93 + 114*x^92 + 117*x^91 + 100*x^90 + 115*x^89 + 6*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 18*x^84 + 73*x^83 + 60*x^82 + 111*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 51*x^75 + 108*x^74 + 69*x^73 + 58*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 62*x^68 + 55*x^67 + 52*x^66 + 49*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 41*x^27 + 52*x^26 + 95*x^25 + 30*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 26*x^20 + 45*x^19 + 108*x^18 + 107*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 23*x^11 + 60*x^10 + x^9 + 50*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 38*x^4 + 107*x^3 + 100*x^2 + 93*x + 18, x^95 + 15*x^93 + 86*x^92 + 37*x^91 + 76*x^90 + 99*x^89 + 18*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 54*x^84 + 89*x^83 + 20*x^82 + 63*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 67*x^75 + 36*x^74 + 21*x^73 + 46*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 58*x^68 + 103*x^67 + 60*x^66 + 33*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 25*x^27 + 60*x^26 + 15*x^25 + 90*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 78*x^20 + 125*x^19 + 36*x^18 + 123*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 103*x^11 + 20*x^10 + 17*x^9 + 22*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 114*x^4 + 91*x^3 + 76*x^2 + 13*x + 54, x^95 + 15*x^93 + 94*x^92 + 101*x^91 + 76*x^90 + 3*x^89 + 26*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 94*x^84 + 25*x^83 + 84*x^82 + 31*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 3*x^75 + 36*x^74 + 117*x^73 + 102*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 18*x^68 + 39*x^67 + 124*x^66 + 65*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 89*x^27 + 60*x^26 + 47*x^25 + 2*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 22*x^20 + 61*x^19 + 100*x^18 + 91*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 39*x^11 + 20*x^10 + 113*x^9 + 110*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 106*x^4 + 27*x^3 + 12*x^2 + 45*x + 46, x^95 + 15*x^93 + 58*x^92 + 85*x^91 + 36*x^90 + 51*x^89 + 14*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 122*x^84 + 105*x^83 + 60*x^82 + 47*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 83*x^75 + 44*x^74 + 5*x^73 + 114*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 86*x^68 + 23*x^67 + 52*x^66 + 113*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 9*x^27 + 116*x^26 + 31*x^25 + 70*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 34*x^20 + 77*x^19 + 108*x^18 + 43*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 55*x^11 + 124*x^10 + 65*x^9 + 10*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 94*x^4 + 75*x^3 + 100*x^2 + 29*x + 10, x^95 + 15*x^93 + 78*x^92 + 37*x^91 + 44*x^90 + 67*x^89 + 106*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 78*x^84 + 89*x^83 + 116*x^82 + 95*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 67*x^75 + 68*x^74 + 53*x^73 + 22*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 34*x^68 + 103*x^67 + 92*x^66 + x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 25*x^27 + 28*x^26 + 111*x^25 + 18*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 70*x^20 + 125*x^19 + 4*x^18 + 27*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 103*x^11 + 52*x^10 + 49*x^9 + 94*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 58*x^4 + 91*x^3 + 108*x^2 + 109*x + 30, x^95 + 15*x^93 + 30*x^92 + 69*x^91 + 12*x^90 + 35*x^89 + 26*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 30*x^84 + 57*x^83 + 20*x^82 + 127*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 35*x^75 + 100*x^74 + 85*x^73 + 102*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 82*x^68 + 7*x^67 + 60*x^66 + 97*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 57*x^27 + 124*x^26 + 79*x^25 + 2*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 86*x^20 + 93*x^19 + 36*x^18 + 59*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 71*x^11 + 84*x^10 + 81*x^9 + 110*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 42*x^4 + 123*x^3 + 76*x^2 + 77*x + 46, x^95 + 15*x^93 + 62*x^92 + 117*x^91 + 60*x^90 + 51*x^89 + 10*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 30*x^84 + 73*x^83 + 36*x^82 + 47*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 51*x^75 + 116*x^74 + 5*x^73 + 54*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 18*x^68 + 55*x^67 + 108*x^66 + 113*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 41*x^27 + 108*x^26 + 31*x^25 + 50*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 86*x^20 + 45*x^19 + 116*x^18 + 43*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 23*x^11 + 36*x^10 + 65*x^9 + 126*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 106*x^4 + 107*x^3 + 60*x^2 + 29*x + 30, x^95 + 15*x^93 + 78*x^92 + 53*x^91 + 92*x^90 + 51*x^89 + 122*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 46*x^84 + 9*x^83 + 4*x^82 + 47*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 115*x^75 + 84*x^74 + 5*x^73 + 70*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 2*x^68 + 119*x^67 + 12*x^66 + 113*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 105*x^27 + 12*x^26 + 31*x^25 + 98*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 38*x^20 + 109*x^19 + 84*x^18 + 43*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 87*x^11 + 4*x^10 + 65*x^9 + 78*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 26*x^4 + 43*x^3 + 92*x^2 + 29*x + 110, x^95 + 15*x^93 + 122*x^92 + 101*x^91 + 116*x^90 + 35*x^89 + 62*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 90*x^84 + 25*x^83 + 44*x^82 + 127*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 3*x^75 + 28*x^74 + 85*x^73 + 2*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 54*x^68 + 39*x^67 + 4*x^66 + 97*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 89*x^27 + 4*x^26 + 79*x^25 + 54*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 2*x^20 + 61*x^19 + 28*x^18 + 59*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 39*x^11 + 44*x^10 + 81*x^9 + 90*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 62*x^4 + 27*x^3 + 116*x^2 + 77*x + 122, x^95 + 15*x^93 + 42*x^92 + 117*x^91 + 68*x^90 + 19*x^89 + 30*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 106*x^84 + 73*x^83 + 28*x^82 + 79*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 51*x^75 + 12*x^74 + 37*x^73 + 98*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 102*x^68 + 55*x^67 + 84*x^66 + 81*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 41*x^27 + 20*x^26 + 127*x^25 + 22*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 82*x^20 + 45*x^19 + 76*x^18 + 75*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 23*x^11 + 92*x^10 + 97*x^9 + 58*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 46*x^4 + 107*x^3 + 4*x^2 + 125*x + 58, x^95 + 15*x^93 + 18*x^92 + 101*x^91 + 20*x^90 + 67*x^89 + 118*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 18*x^84 + 25*x^83 + 76*x^82 + 95*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 3*x^75 + 124*x^74 + 53*x^73 + 10*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 126*x^68 + 39*x^67 + 100*x^66 + x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 89*x^27 + 36*x^26 + 111*x^25 + 78*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 26*x^20 + 61*x^19 + 60*x^18 + 27*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 39*x^11 + 12*x^10 + 49*x^9 + 66*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 102*x^4 + 27*x^3 + 84*x^2 + 109*x + 2, x^95 + 15*x^93 + 2*x^92 + 21*x^91 + 4*x^90 + 83*x^89 + 54*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 34*x^84 + 41*x^83 + 28*x^82 + 15*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 19*x^75 + 76*x^74 + 101*x^73 + 10*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 46*x^68 + 87*x^67 + 84*x^66 + 17*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 73*x^27 + 84*x^26 + 63*x^25 + 14*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 106*x^20 + 13*x^19 + 76*x^18 + 11*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 119*x^11 + 28*x^10 + 33*x^9 + 66*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 86*x^4 + 11*x^3 + 4*x^2 + 61*x + 34, x^95 + 15*x^93 + 122*x^92 + 53*x^91 + 68*x^90 + 19*x^89 + 110*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 122*x^84 + 9*x^83 + 28*x^82 + 79*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 115*x^75 + 12*x^74 + 37*x^73 + 18*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 86*x^68 + 119*x^67 + 84*x^66 + 81*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 105*x^27 + 20*x^26 + 127*x^25 + 38*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 34*x^20 + 109*x^19 + 76*x^18 + 75*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 87*x^11 + 92*x^10 + 97*x^9 + 42*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 94*x^4 + 43*x^3 + 4*x^2 + 125*x + 106, x^95 + 15*x^93 + 90*x^92 + 53*x^91 + 68*x^90 + 83*x^89 + 14*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 90*x^84 + 9*x^83 + 28*x^82 + 15*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 115*x^75 + 12*x^74 + 101*x^73 + 114*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 118*x^68 + 119*x^67 + 84*x^66 + 17*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 105*x^27 + 20*x^26 + 63*x^25 + 70*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 2*x^20 + 109*x^19 + 76*x^18 + 11*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 87*x^11 + 92*x^10 + 33*x^9 + 10*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 126*x^4 + 43*x^3 + 4*x^2 + 61*x + 74, x^95 + 15*x^93 + 58*x^92 + 85*x^91 + 68*x^90 + 51*x^89 + 110*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 58*x^84 + 105*x^83 + 28*x^82 + 47*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 83*x^75 + 12*x^74 + 5*x^73 + 18*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 22*x^68 + 23*x^67 + 84*x^66 + 113*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 9*x^27 + 20*x^26 + 31*x^25 + 38*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 98*x^20 + 77*x^19 + 76*x^18 + 43*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 55*x^11 + 92*x^10 + 65*x^9 + 42*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 30*x^4 + 75*x^3 + 4*x^2 + 29*x + 106, x^95 + 15*x^93 + 94*x^92 + 21*x^91 + 124*x^90 + 19*x^89 + 106*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 62*x^84 + 41*x^83 + 100*x^82 + 79*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 19*x^75 + 52*x^74 + 37*x^73 + 86*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 114*x^68 + 87*x^67 + 44*x^66 + 81*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 73*x^27 + 44*x^26 + 127*x^25 + 18*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 118*x^20 + 13*x^19 + 52*x^18 + 75*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 119*x^11 + 100*x^10 + 97*x^9 + 30*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 74*x^4 + 11*x^3 + 124*x^2 + 125*x + 62, x^95 + 15*x^93 + 114*x^92 + 101*x^91 + 52*x^90 + 67*x^89 + 54*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 50*x^84 + 25*x^83 + 44*x^82 + 95*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 3*x^75 + 92*x^74 + 53*x^73 + 74*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 94*x^68 + 39*x^67 + 4*x^66 + x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 89*x^27 + 68*x^26 + 111*x^25 + 14*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 58*x^20 + 61*x^19 + 28*x^18 + 27*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 39*x^11 + 108*x^10 + 49*x^9 + 2*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 70*x^4 + 27*x^3 + 116*x^2 + 109*x + 2, x^95 + 15*x^93 + 70*x^92 + 85*x^91 + 92*x^90 + 115*x^89 + 50*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 6*x^84 + 105*x^83 + 68*x^82 + 111*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 83*x^75 + 84*x^74 + 69*x^73 + 78*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 42*x^68 + 23*x^67 + 76*x^66 + 49*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 9*x^27 + 12*x^26 + 95*x^25 + 122*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 94*x^20 + 77*x^19 + 20*x^18 + 107*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 55*x^11 + 4*x^10 + x^9 + 54*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 34*x^4 + 75*x^3 + 28*x^2 + 93*x + 54, x^95 + 15*x^93 + 54*x^92 + 101*x^91 + 76*x^90 + 35*x^89 + 114*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 22*x^84 + 25*x^83 + 20*x^82 + 127*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 3*x^75 + 36*x^74 + 85*x^73 + 78*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 90*x^68 + 39*x^67 + 60*x^66 + 97*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 89*x^27 + 60*x^26 + 79*x^25 + 58*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 46*x^20 + 61*x^19 + 36*x^18 + 59*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 39*x^11 + 20*x^10 + 81*x^9 + 54*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 18*x^4 + 27*x^3 + 76*x^2 + 77*x + 86, x^95 + 15*x^93 + 74*x^92 + 53*x^91 + 100*x^90 + 19*x^89 + 94*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 74*x^84 + 9*x^83 + 124*x^82 + 79*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 115*x^75 + 108*x^74 + 37*x^73 + 34*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 6*x^68 + 119*x^67 + 116*x^66 + 81*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 105*x^27 + 52*x^26 + 127*x^25 + 86*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 50*x^20 + 109*x^19 + 44*x^18 + 75*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 87*x^11 + 60*x^10 + 97*x^9 + 122*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 78*x^4 + 43*x^3 + 36*x^2 + 125*x + 58, x^95 + 15*x^93 + 106*x^92 + 21*x^91 + 4*x^90 + 51*x^89 + 94*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 42*x^84 + 41*x^83 + 92*x^82 + 47*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 19*x^75 + 76*x^74 + 5*x^73 + 34*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 38*x^68 + 87*x^67 + 20*x^66 + 113*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 73*x^27 + 84*x^26 + 31*x^25 + 86*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 18*x^20 + 13*x^19 + 12*x^18 + 43*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 119*x^11 + 28*x^10 + 65*x^9 + 122*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 110*x^4 + 11*x^3 + 68*x^2 + 29*x + 122, x^95 + 15*x^93 + 98*x^92 + 21*x^91 + 4*x^90 + 83*x^89 + 22*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 2*x^84 + 41*x^83 + 28*x^82 + 15*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 19*x^75 + 76*x^74 + 101*x^73 + 42*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 78*x^68 + 87*x^67 + 84*x^66 + 17*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 73*x^27 + 84*x^26 + 63*x^25 + 110*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 74*x^20 + 13*x^19 + 76*x^18 + 11*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 119*x^11 + 28*x^10 + 33*x^9 + 98*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 118*x^4 + 11*x^3 + 4*x^2 + 61*x + 66, x^95 + 15*x^93 + 10*x^92 + 53*x^91 + 100*x^90 + 83*x^89 + 94*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 10*x^84 + 9*x^83 + 124*x^82 + 15*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 115*x^75 + 108*x^74 + 101*x^73 + 34*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 70*x^68 + 119*x^67 + 116*x^66 + 17*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 105*x^27 + 52*x^26 + 63*x^25 + 86*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 114*x^20 + 109*x^19 + 44*x^18 + 11*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 87*x^11 + 60*x^10 + 33*x^9 + 122*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 14*x^4 + 43*x^3 + 36*x^2 + 61*x + 58, x^95 + 15*x^93 + 6*x^92 + 69*x^91 + 44*x^90 + 3*x^89 + 98*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 102*x^84 + 57*x^83 + 52*x^82 + 31*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 35*x^75 + 68*x^74 + 117*x^73 + 94*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 10*x^68 + 7*x^67 + 28*x^66 + 65*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 57*x^27 + 28*x^26 + 47*x^25 + 106*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 62*x^20 + 93*x^19 + 68*x^18 + 91*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 71*x^11 + 52*x^10 + 113*x^9 + 6*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 2*x^4 + 123*x^3 + 44*x^2 + 45*x + 38, x^95 + 15*x^93 + 82*x^92 + 21*x^91 + 100*x^90 + 19*x^89 + 38*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 114*x^84 + 41*x^83 + 60*x^82 + 79*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 19*x^75 + 108*x^74 + 37*x^73 + 26*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 94*x^68 + 87*x^67 + 52*x^66 + 81*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 73*x^27 + 52*x^26 + 127*x^25 + 62*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 122*x^20 + 13*x^19 + 108*x^18 + 75*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 119*x^11 + 60*x^10 + 97*x^9 + 18*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 70*x^4 + 11*x^3 + 100*x^2 + 125*x + 114, x^95 + 15*x^93 + 114*x^92 + 37*x^91 + 84*x^90 + 3*x^89 + 22*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 114*x^84 + 89*x^83 + 12*x^82 + 31*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 67*x^75 + 60*x^74 + 117*x^73 + 106*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 30*x^68 + 103*x^67 + 36*x^66 + 65*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 25*x^27 + 100*x^26 + 47*x^25 + 110*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 122*x^20 + 125*x^19 + 124*x^18 + 91*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 103*x^11 + 76*x^10 + 113*x^9 + 34*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 6*x^4 + 91*x^3 + 20*x^2 + 45*x + 98, x^95 + 15*x^93 + 98*x^92 + 85*x^91 + 4*x^90 + 19*x^89 + 22*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 2*x^84 + 105*x^83 + 28*x^82 + 79*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 83*x^75 + 76*x^74 + 37*x^73 + 42*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 78*x^68 + 23*x^67 + 84*x^66 + 81*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 9*x^27 + 84*x^26 + 127*x^25 + 110*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 74*x^20 + 77*x^19 + 76*x^18 + 75*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 55*x^11 + 28*x^10 + 97*x^9 + 98*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 118*x^4 + 75*x^3 + 4*x^2 + 125*x + 66, x^95 + 15*x^93 + 66*x^92 + 5*x^91 + 52*x^90 + 99*x^89 + 6*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 66*x^84 + 121*x^83 + 44*x^82 + 63*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 99*x^75 + 92*x^74 + 21*x^73 + 122*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 78*x^68 + 71*x^67 + 4*x^66 + 33*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 121*x^27 + 68*x^26 + 15*x^25 + 30*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 10*x^20 + 29*x^19 + 28*x^18 + 123*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 7*x^11 + 108*x^10 + 17*x^9 + 114*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 118*x^4 + 59*x^3 + 116*x^2 + 13*x + 50, x^95 + 15*x^93 + 86*x^92 + 69*x^91 + 44*x^90 + 67*x^89 + 50*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 118*x^84 + 57*x^83 + 52*x^82 + 95*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 35*x^75 + 68*x^74 + 53*x^73 + 14*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 122*x^68 + 7*x^67 + 28*x^66 + x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 57*x^27 + 28*x^26 + 111*x^25 + 122*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 14*x^20 + 93*x^19 + 68*x^18 + 27*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 71*x^11 + 52*x^10 + 49*x^9 + 118*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 50*x^4 + 123*x^3 + 44*x^2 + 109*x + 86, x^95 + 15*x^93 + 26*x^92 + 69*x^91 + 52*x^90 + 3*x^89 + 94*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 122*x^84 + 57*x^83 + 108*x^82 + 31*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 35*x^75 + 92*x^74 + 117*x^73 + 98*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 22*x^68 + 7*x^67 + 68*x^66 + 65*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 57*x^27 + 68*x^26 + 47*x^25 + 86*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 34*x^20 + 93*x^19 + 92*x^18 + 91*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 71*x^11 + 108*x^10 + 113*x^9 + 58*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 30*x^4 + 123*x^3 + 52*x^2 + 45*x + 90, x^95 + 15*x^93 + 126*x^92 + 85*x^91 + 124*x^90 + 19*x^89 + 74*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 94*x^84 + 105*x^83 + 100*x^82 + 79*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 83*x^75 + 52*x^74 + 37*x^73 + 118*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 82*x^68 + 23*x^67 + 44*x^66 + 81*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 9*x^27 + 44*x^26 + 127*x^25 + 114*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 22*x^20 + 77*x^19 + 52*x^18 + 75*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 55*x^11 + 100*x^10 + 97*x^9 + 62*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 42*x^4 + 75*x^3 + 124*x^2 + 125*x + 94, x^95 + 15*x^93 + 122*x^92 + 21*x^91 + 36*x^90 + 51*x^89 + 14*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 58*x^84 + 41*x^83 + 60*x^82 + 47*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 19*x^75 + 44*x^74 + 5*x^73 + 114*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 22*x^68 + 87*x^67 + 52*x^66 + 113*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 73*x^27 + 116*x^26 + 31*x^25 + 70*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 98*x^20 + 13*x^19 + 108*x^18 + 43*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 119*x^11 + 124*x^10 + 65*x^9 + 10*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 30*x^4 + 11*x^3 + 100*x^2 + 29*x + 10, x^95 + 15*x^93 + 14*x^92 + 53*x^91 + 92*x^90 + 115*x^89 + 122*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 110*x^84 + 9*x^83 + 4*x^82 + 111*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 115*x^75 + 84*x^74 + 69*x^73 + 70*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 66*x^68 + 119*x^67 + 12*x^66 + 49*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 105*x^27 + 12*x^26 + 95*x^25 + 98*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 102*x^20 + 109*x^19 + 84*x^18 + 107*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 87*x^11 + 4*x^10 + x^9 + 78*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 90*x^4 + 43*x^3 + 92*x^2 + 93*x + 110, x^95 + 15*x^93 + 86*x^92 + 117*x^91 + 28*x^90 + 19*x^89 + 2*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 86*x^84 + 73*x^83 + 4*x^82 + 79*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 51*x^75 + 20*x^74 + 37*x^73 + 126*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 90*x^68 + 55*x^67 + 12*x^66 + 81*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 41*x^27 + 76*x^26 + 127*x^25 + 10*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 110*x^20 + 45*x^19 + 84*x^18 + 75*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 23*x^11 + 68*x^10 + 97*x^9 + 38*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 18*x^4 + 107*x^3 + 92*x^2 + 125*x + 102, x^95 + 15*x^93 + 34*x^92 + 69*x^91 + 20*x^90 + 99*x^89 + 70*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 98*x^84 + 57*x^83 + 76*x^82 + 63*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 35*x^75 + 124*x^74 + 21*x^73 + 58*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 46*x^68 + 7*x^67 + 100*x^66 + 33*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 57*x^27 + 36*x^26 + 15*x^25 + 94*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 42*x^20 + 93*x^19 + 60*x^18 + 123*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 71*x^11 + 12*x^10 + 17*x^9 + 50*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 86*x^4 + 123*x^3 + 84*x^2 + 13*x + 50, x^95 + 15*x^93 + 126*x^92 + 37*x^91 + 44*x^90 + 3*x^89 + 26*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 62*x^84 + 89*x^83 + 116*x^82 + 31*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 67*x^75 + 68*x^74 + 117*x^73 + 102*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 50*x^68 + 103*x^67 + 92*x^66 + 65*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 25*x^27 + 28*x^26 + 47*x^25 + 2*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 118*x^20 + 125*x^19 + 4*x^18 + 91*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 103*x^11 + 52*x^10 + 113*x^9 + 110*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 10*x^4 + 91*x^3 + 108*x^2 + 45*x + 110, x^95 + 15*x^93 + 22*x^92 + 53*x^91 + 60*x^90 + 83*x^89 + 34*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 86*x^84 + 9*x^83 + 100*x^82 + 15*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 115*x^75 + 116*x^74 + 101*x^73 + 94*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 90*x^68 + 119*x^67 + 44*x^66 + 17*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 105*x^27 + 108*x^26 + 63*x^25 + 42*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 110*x^20 + 109*x^19 + 52*x^18 + 11*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 87*x^11 + 36*x^10 + 33*x^9 + 6*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 18*x^4 + 43*x^3 + 124*x^2 + 61*x + 6, x^95 + 15*x^93 + 114*x^92 + 117*x^91 + 36*x^90 + 115*x^89 + 70*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 18*x^84 + 73*x^83 + 124*x^82 + 111*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 51*x^75 + 44*x^74 + 69*x^73 + 122*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 62*x^68 + 55*x^67 + 116*x^66 + 49*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 41*x^27 + 116*x^26 + 95*x^25 + 94*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 26*x^20 + 45*x^19 + 44*x^18 + 107*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 23*x^11 + 124*x^10 + x^9 + 114*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 38*x^4 + 107*x^3 + 36*x^2 + 93*x + 82, x^95 + 15*x^93 + 46*x^92 + 117*x^91 + 60*x^90 + 51*x^89 + 58*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 78*x^84 + 73*x^83 + 36*x^82 + 47*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 51*x^75 + 116*x^74 + 5*x^73 + 6*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 98*x^68 + 55*x^67 + 108*x^66 + 113*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 41*x^27 + 108*x^26 + 31*x^25 + 34*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 70*x^20 + 45*x^19 + 116*x^18 + 43*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 23*x^11 + 36*x^10 + 65*x^9 + 14*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 122*x^4 + 107*x^3 + 60*x^2 + 29*x + 110, x^95 + 15*x^93 + 82*x^92 + 69*x^91 + 84*x^90 + 35*x^89 + 54*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 82*x^84 + 57*x^83 + 12*x^82 + 127*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 35*x^75 + 60*x^74 + 85*x^73 + 74*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 62*x^68 + 7*x^67 + 36*x^66 + 97*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 57*x^27 + 100*x^26 + 79*x^25 + 14*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 90*x^20 + 93*x^19 + 124*x^18 + 59*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 71*x^11 + 76*x^10 + 81*x^9 + 2*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 38*x^4 + 123*x^3 + 20*x^2 + 77*x + 66, x^95 + 15*x^93 + 86*x^92 + 85*x^91 + 124*x^90 + 51*x^89 + 34*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 22*x^84 + 105*x^83 + 36*x^82 + 47*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 83*x^75 + 52*x^74 + 5*x^73 + 94*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 26*x^68 + 23*x^67 + 108*x^66 + 113*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 9*x^27 + 44*x^26 + 31*x^25 + 42*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 46*x^20 + 77*x^19 + 116*x^18 + 43*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 55*x^11 + 100*x^10 + 65*x^9 + 6*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 82*x^4 + 75*x^3 + 60*x^2 + 29*x + 6, x^95 + 15*x^93 + 42*x^92 + 53*x^91 + 100*x^90 + 83*x^89 + 126*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 42*x^84 + 9*x^83 + 124*x^82 + 15*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 115*x^75 + 108*x^74 + 101*x^73 + 2*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 38*x^68 + 119*x^67 + 116*x^66 + 17*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 105*x^27 + 52*x^26 + 63*x^25 + 118*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 18*x^20 + 109*x^19 + 44*x^18 + 11*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 87*x^11 + 60*x^10 + 33*x^9 + 90*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 110*x^4 + 43*x^3 + 36*x^2 + 61*x + 26, x^95 + 15*x^93 + 90*x^92 + 37*x^91 + 116*x^90 + 99*x^89 + 30*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 58*x^84 + 89*x^83 + 44*x^82 + 63*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 67*x^75 + 28*x^74 + 21*x^73 + 34*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 86*x^68 + 103*x^67 + 4*x^66 + 33*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 25*x^27 + 4*x^26 + 15*x^25 + 22*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 98*x^20 + 125*x^19 + 28*x^18 + 123*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 103*x^11 + 44*x^10 + 17*x^9 + 122*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 94*x^4 + 91*x^3 + 116*x^2 + 13*x + 26, x^95 + 15*x^93 + 14*x^92 + 5*x^91 + 12*x^90 + 35*x^89 + 10*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 78*x^84 + 121*x^83 + 20*x^82 + 127*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 99*x^75 + 100*x^74 + 85*x^73 + 118*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 34*x^68 + 71*x^67 + 60*x^66 + 97*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 121*x^27 + 124*x^26 + 79*x^25 + 50*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 70*x^20 + 29*x^19 + 36*x^18 + 59*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 7*x^11 + 84*x^10 + 81*x^9 + 62*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 58*x^4 + 59*x^3 + 76*x^2 + 77*x + 62, x^95 + 15*x^93 + 18*x^92 + 53*x^91 + 68*x^90 + 51*x^89 + 70*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 114*x^84 + 9*x^83 + 92*x^82 + 47*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 115*x^75 + 12*x^74 + 5*x^73 + 122*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 94*x^68 + 119*x^67 + 20*x^66 + 113*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 105*x^27 + 20*x^26 + 31*x^25 + 94*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 122*x^20 + 109*x^19 + 12*x^18 + 43*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 87*x^11 + 92*x^10 + 65*x^9 + 114*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 70*x^4 + 43*x^3 + 68*x^2 + 29*x + 18, x^95 + 15*x^93 + 98*x^92 + 37*x^91 + 84*x^90 + 67*x^89 + 6*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 34*x^84 + 89*x^83 + 12*x^82 + 95*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 67*x^75 + 60*x^74 + 53*x^73 + 122*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 110*x^68 + 103*x^67 + 36*x^66 + x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 25*x^27 + 100*x^26 + 111*x^25 + 30*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 106*x^20 + 125*x^19 + 124*x^18 + 27*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 103*x^11 + 76*x^10 + 49*x^9 + 114*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 22*x^4 + 91*x^3 + 20*x^2 + 109*x + 114, x^95 + 15*x^93 + 74*x^92 + 101*x^91 + 116*x^90 + 35*x^89 + 78*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 106*x^84 + 25*x^83 + 44*x^82 + 127*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 3*x^75 + 28*x^74 + 85*x^73 + 114*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 38*x^68 + 39*x^67 + 4*x^66 + 97*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 89*x^27 + 4*x^26 + 79*x^25 + 6*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 82*x^20 + 61*x^19 + 28*x^18 + 59*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 39*x^11 + 44*x^10 + 81*x^9 + 10*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 110*x^4 + 27*x^3 + 116*x^2 + 77*x + 106, x^95 + 15*x^93 + 118*x^92 + 53*x^91 + 124*x^90 + 19*x^89 + 2*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 54*x^84 + 9*x^83 + 36*x^82 + 79*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 115*x^75 + 52*x^74 + 37*x^73 + 126*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 122*x^68 + 119*x^67 + 108*x^66 + 81*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 105*x^27 + 44*x^26 + 127*x^25 + 10*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 78*x^20 + 109*x^19 + 116*x^18 + 75*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 87*x^11 + 100*x^10 + 97*x^9 + 38*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 50*x^4 + 43*x^3 + 60*x^2 + 125*x + 38, x^95 + 15*x^93 + 86*x^92 + 117*x^91 + 60*x^90 + 19*x^89 + 98*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 22*x^84 + 73*x^83 + 100*x^82 + 79*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 51*x^75 + 116*x^74 + 37*x^73 + 30*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 26*x^68 + 55*x^67 + 44*x^66 + 81*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 41*x^27 + 108*x^26 + 127*x^25 + 106*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 46*x^20 + 45*x^19 + 52*x^18 + 75*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 23*x^11 + 36*x^10 + 97*x^9 + 70*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 82*x^4 + 107*x^3 + 124*x^2 + 125*x + 70, x^95 + 15*x^93 + 74*x^92 + 5*x^91 + 52*x^90 + 67*x^89 + 78*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 106*x^84 + 121*x^83 + 108*x^82 + 95*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 99*x^75 + 92*x^74 + 53*x^73 + 114*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 38*x^68 + 71*x^67 + 68*x^66 + x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 121*x^27 + 68*x^26 + 111*x^25 + 6*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 82*x^20 + 29*x^19 + 92*x^18 + 27*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 7*x^11 + 108*x^10 + 49*x^9 + 10*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 110*x^4 + 59*x^3 + 52*x^2 + 109*x + 106, x^95 + 15*x^93 + 30*x^92 + 5*x^91 + 44*x^90 + 35*x^89 + 58*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 94*x^84 + 121*x^83 + 116*x^82 + 127*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 99*x^75 + 68*x^74 + 85*x^73 + 70*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 18*x^68 + 71*x^67 + 92*x^66 + 97*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 121*x^27 + 28*x^26 + 79*x^25 + 34*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 22*x^20 + 29*x^19 + 4*x^18 + 59*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 7*x^11 + 52*x^10 + 81*x^9 + 78*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 106*x^4 + 59*x^3 + 108*x^2 + 77*x + 78, x^95 + 15*x^93 + 46*x^92 + 5*x^91 + 108*x^90 + 35*x^89 + 74*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 46*x^84 + 121*x^83 + 52*x^82 + 127*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 99*x^75 + 4*x^74 + 85*x^73 + 54*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 66*x^68 + 71*x^67 + 28*x^66 + 97*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 121*x^27 + 92*x^26 + 79*x^25 + 114*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 38*x^20 + 29*x^19 + 68*x^18 + 59*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 7*x^11 + 116*x^10 + 81*x^9 + 126*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 90*x^4 + 59*x^3 + 44*x^2 + 77*x + 62, x^95 + 15*x^93 + 38*x^92 + 101*x^91 + 12*x^90 + 35*x^89 + 98*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 70*x^84 + 25*x^83 + 84*x^82 + 127*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 3*x^75 + 100*x^74 + 85*x^73 + 94*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 42*x^68 + 39*x^67 + 124*x^66 + 97*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 89*x^27 + 124*x^26 + 79*x^25 + 106*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 30*x^20 + 61*x^19 + 100*x^18 + 59*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 39*x^11 + 84*x^10 + 81*x^9 + 6*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 34*x^4 + 27*x^3 + 12*x^2 + 77*x + 102, x^95 + 15*x^93 + 30*x^92 + 5*x^91 + 108*x^90 + 99*x^89 + 58*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 94*x^84 + 121*x^83 + 52*x^82 + 63*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 99*x^75 + 4*x^74 + 21*x^73 + 70*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 18*x^68 + 71*x^67 + 28*x^66 + 33*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 121*x^27 + 92*x^26 + 15*x^25 + 34*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 22*x^20 + 29*x^19 + 68*x^18 + 123*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 7*x^11 + 116*x^10 + 17*x^9 + 78*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 106*x^4 + 59*x^3 + 44*x^2 + 13*x + 78, x^95 + 15*x^93 + 46*x^92 + 69*x^91 + 12*x^90 + 35*x^89 + 106*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 110*x^84 + 57*x^83 + 20*x^82 + 127*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 35*x^75 + 100*x^74 + 85*x^73 + 22*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 2*x^68 + 7*x^67 + 60*x^66 + 97*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 57*x^27 + 124*x^26 + 79*x^25 + 18*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 102*x^20 + 93*x^19 + 36*x^18 + 59*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 71*x^11 + 84*x^10 + 81*x^9 + 94*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 26*x^4 + 123*x^3 + 76*x^2 + 77*x + 94, x^95 + 15*x^93 + 18*x^92 + 53*x^91 + 36*x^90 + 115*x^89 + 38*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 50*x^84 + 9*x^83 + 124*x^82 + 111*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 115*x^75 + 44*x^74 + 69*x^73 + 26*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 30*x^68 + 119*x^67 + 116*x^66 + 49*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 105*x^27 + 116*x^26 + 95*x^25 + 62*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 58*x^20 + 109*x^19 + 44*x^18 + 107*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 87*x^11 + 124*x^10 + x^9 + 18*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 6*x^4 + 43*x^3 + 36*x^2 + 93*x + 114, x^95 + 15*x^93 + 2*x^92 + 101*x^91 + 20*x^90 + 3*x^89 + 102*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 66*x^84 + 25*x^83 + 76*x^82 + 31*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 3*x^75 + 124*x^74 + 117*x^73 + 26*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 78*x^68 + 39*x^67 + 100*x^66 + 65*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 89*x^27 + 36*x^26 + 47*x^25 + 126*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 10*x^20 + 61*x^19 + 60*x^18 + 91*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 39*x^11 + 12*x^10 + 113*x^9 + 18*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 118*x^4 + 27*x^3 + 84*x^2 + 45*x + 18, x^95 + 15*x^93 + 74*x^92 + 117*x^91 + 4*x^90 + 83*x^89 + 62*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 10*x^84 + 73*x^83 + 92*x^82 + 15*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 51*x^75 + 76*x^74 + 101*x^73 + 66*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 70*x^68 + 55*x^67 + 20*x^66 + 17*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 41*x^27 + 84*x^26 + 63*x^25 + 54*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 114*x^20 + 45*x^19 + 12*x^18 + 11*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 23*x^11 + 28*x^10 + 33*x^9 + 26*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 14*x^4 + 107*x^3 + 68*x^2 + 61*x + 26, x^95 + 15*x^93 + 78*x^92 + 117*x^91 + 60*x^90 + 115*x^89 + 26*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 110*x^84 + 73*x^83 + 36*x^82 + 111*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 51*x^75 + 116*x^74 + 69*x^73 + 38*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 66*x^68 + 55*x^67 + 108*x^66 + 49*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 41*x^27 + 108*x^26 + 95*x^25 + 2*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 102*x^20 + 45*x^19 + 116*x^18 + 107*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 23*x^11 + 36*x^10 + x^9 + 46*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 90*x^4 + 107*x^3 + 60*x^2 + 93*x + 14, x^95 + 15*x^93 + 62*x^92 + 53*x^91 + 28*x^90 + 51*x^89 + 106*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 94*x^84 + 9*x^83 + 68*x^82 + 47*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 115*x^75 + 20*x^74 + 5*x^73 + 86*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 82*x^68 + 119*x^67 + 76*x^66 + 113*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 105*x^27 + 76*x^26 + 31*x^25 + 18*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 22*x^20 + 109*x^19 + 20*x^18 + 43*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 87*x^11 + 68*x^10 + 65*x^9 + 30*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 42*x^4 + 43*x^3 + 28*x^2 + 29*x + 126, x^95 + 15*x^93 + 98*x^92 + 37*x^91 + 116*x^90 + 3*x^89 + 38*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 98*x^84 + 89*x^83 + 108*x^82 + 31*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 67*x^75 + 28*x^74 + 117*x^73 + 90*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 46*x^68 + 103*x^67 + 68*x^66 + 65*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 25*x^27 + 4*x^26 + 47*x^25 + 62*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 42*x^20 + 125*x^19 + 92*x^18 + 91*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 103*x^11 + 44*x^10 + 113*x^9 + 82*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 86*x^4 + 91*x^3 + 52*x^2 + 45*x + 18, x^95 + 15*x^93 + 34*x^92 + 37*x^91 + 116*x^90 + 67*x^89 + 38*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 34*x^84 + 89*x^83 + 108*x^82 + 95*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 67*x^75 + 28*x^74 + 53*x^73 + 90*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 110*x^68 + 103*x^67 + 68*x^66 + x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 25*x^27 + 4*x^26 + 111*x^25 + 62*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 106*x^20 + 125*x^19 + 92*x^18 + 27*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 103*x^11 + 44*x^10 + 49*x^9 + 82*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 22*x^4 + 91*x^3 + 52*x^2 + 109*x + 18, x^95 + 15*x^93 + 114*x^92 + 53*x^91 + 4*x^90 + 51*x^89 + 102*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 82*x^84 + 9*x^83 + 28*x^82 + 47*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 115*x^75 + 76*x^74 + 5*x^73 + 90*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 126*x^68 + 119*x^67 + 84*x^66 + 113*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 105*x^27 + 84*x^26 + 31*x^25 + 126*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 90*x^20 + 109*x^19 + 76*x^18 + 43*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 87*x^11 + 28*x^10 + 65*x^9 + 82*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 102*x^4 + 43*x^3 + 4*x^2 + 29*x + 114, x^95 + 15*x^93 + 18*x^92 + 5*x^91 + 52*x^90 + 35*x^89 + 86*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 82*x^84 + 121*x^83 + 44*x^82 + 127*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 99*x^75 + 92*x^74 + 85*x^73 + 42*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 62*x^68 + 71*x^67 + 4*x^66 + 97*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 121*x^27 + 68*x^26 + 79*x^25 + 46*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 90*x^20 + 29*x^19 + 28*x^18 + 59*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 7*x^11 + 108*x^10 + 81*x^9 + 98*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 38*x^4 + 59*x^3 + 116*x^2 + 77*x + 98, x^95 + 15*x^93 + 102*x^92 + 85*x^91 + 124*x^90 + 51*x^89 + 114*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 102*x^84 + 105*x^83 + 36*x^82 + 47*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 83*x^75 + 52*x^74 + 5*x^73 + 14*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 74*x^68 + 23*x^67 + 108*x^66 + 113*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 9*x^27 + 44*x^26 + 31*x^25 + 58*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 62*x^20 + 77*x^19 + 116*x^18 + 43*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 55*x^11 + 100*x^10 + 65*x^9 + 118*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 66*x^4 + 75*x^3 + 60*x^2 + 29*x + 54, x^95 + 15*x^93 + 126*x^92 + 69*x^91 + 108*x^90 + 35*x^89 + 26*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 62*x^84 + 57*x^83 + 52*x^82 + 127*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 35*x^75 + 4*x^74 + 85*x^73 + 102*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 50*x^68 + 7*x^67 + 28*x^66 + 97*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 57*x^27 + 92*x^26 + 79*x^25 + 2*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 118*x^20 + 93*x^19 + 68*x^18 + 59*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 71*x^11 + 116*x^10 + 81*x^9 + 110*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 10*x^4 + 123*x^3 + 44*x^2 + 77*x + 110, x^95 + 15*x^93 + 2*x^92 + 5*x^91 + 116*x^90 + 99*x^89 + 6*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 2*x^84 + 121*x^83 + 108*x^82 + 63*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 99*x^75 + 28*x^74 + 21*x^73 + 122*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 14*x^68 + 71*x^67 + 68*x^66 + 33*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 121*x^27 + 4*x^26 + 15*x^25 + 30*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 74*x^20 + 29*x^19 + 92*x^18 + 123*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 7*x^11 + 44*x^10 + 17*x^9 + 114*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 54*x^4 + 59*x^3 + 52*x^2 + 13*x + 50, x^95 + 15*x^93 + 90*x^92 + 117*x^91 + 68*x^90 + 19*x^89 + 14*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 90*x^84 + 73*x^83 + 28*x^82 + 79*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 51*x^75 + 12*x^74 + 37*x^73 + 114*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 118*x^68 + 55*x^67 + 84*x^66 + 81*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 41*x^27 + 20*x^26 + 127*x^25 + 70*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 2*x^20 + 45*x^19 + 76*x^18 + 75*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 23*x^11 + 92*x^10 + 97*x^9 + 10*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 126*x^4 + 107*x^3 + 4*x^2 + 125*x + 74, x^95 + 15*x^93 + 98*x^92 + 101*x^91 + 116*x^90 + 67*x^89 + 38*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 98*x^84 + 25*x^83 + 108*x^82 + 95*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 3*x^75 + 28*x^74 + 53*x^73 + 90*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 46*x^68 + 39*x^67 + 68*x^66 + x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 89*x^27 + 4*x^26 + 111*x^25 + 62*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 42*x^20 + 61*x^19 + 92*x^18 + 27*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 39*x^11 + 44*x^10 + 49*x^9 + 82*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 86*x^4 + 27*x^3 + 52*x^2 + 109*x + 18, x^95 + 15*x^93 + 78*x^92 + 69*x^91 + 76*x^90 + 99*x^89 + 10*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 14*x^84 + 57*x^83 + 84*x^82 + 63*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 35*x^75 + 36*x^74 + 21*x^73 + 118*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 98*x^68 + 7*x^67 + 124*x^66 + 33*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 57*x^27 + 60*x^26 + 15*x^25 + 50*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 6*x^20 + 93*x^19 + 100*x^18 + 123*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 71*x^11 + 20*x^10 + 17*x^9 + 62*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 122*x^4 + 123*x^3 + 12*x^2 + 13*x + 62, x^95 + 15*x^93 + 70*x^92 + 85*x^91 + 124*x^90 + 115*x^89 + 18*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 70*x^84 + 105*x^83 + 36*x^82 + 111*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 83*x^75 + 52*x^74 + 69*x^73 + 110*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 106*x^68 + 23*x^67 + 108*x^66 + 49*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 9*x^27 + 44*x^26 + 95*x^25 + 90*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 30*x^20 + 77*x^19 + 116*x^18 + 107*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 55*x^11 + 100*x^10 + x^9 + 86*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 98*x^4 + 75*x^3 + 60*x^2 + 93*x + 22, x^95 + 15*x^93 + 30*x^92 + 5*x^91 + 76*x^90 + 35*x^89 + 26*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 30*x^84 + 121*x^83 + 84*x^82 + 127*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 99*x^75 + 36*x^74 + 85*x^73 + 102*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 82*x^68 + 71*x^67 + 124*x^66 + 97*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 121*x^27 + 60*x^26 + 79*x^25 + 2*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 86*x^20 + 29*x^19 + 100*x^18 + 59*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 7*x^11 + 20*x^10 + 81*x^9 + 110*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 42*x^4 + 59*x^3 + 12*x^2 + 77*x + 46, x^95 + 15*x^93 + 74*x^92 + 117*x^91 + 36*x^90 + 19*x^89 + 94*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 74*x^84 + 73*x^83 + 60*x^82 + 79*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 51*x^75 + 44*x^74 + 37*x^73 + 34*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 6*x^68 + 55*x^67 + 52*x^66 + 81*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 41*x^27 + 116*x^26 + 127*x^25 + 86*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 50*x^20 + 45*x^19 + 108*x^18 + 75*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 23*x^11 + 124*x^10 + 97*x^9 + 122*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 78*x^4 + 107*x^3 + 100*x^2 + 125*x + 58, x^95 + 15*x^93 + 126*x^92 + 117*x^91 + 60*x^90 + 115*x^89 + 10*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 94*x^84 + 73*x^83 + 36*x^82 + 111*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 51*x^75 + 116*x^74 + 69*x^73 + 54*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 82*x^68 + 55*x^67 + 108*x^66 + 49*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 41*x^27 + 108*x^26 + 95*x^25 + 50*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 22*x^20 + 45*x^19 + 116*x^18 + 107*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 23*x^11 + 36*x^10 + x^9 + 126*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 42*x^4 + 107*x^3 + 60*x^2 + 93*x + 30, x^95 + 15*x^93 + 126*x^92 + 21*x^91 + 60*x^90 + 83*x^89 + 10*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 94*x^84 + 41*x^83 + 36*x^82 + 15*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 19*x^75 + 116*x^74 + 101*x^73 + 54*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 82*x^68 + 87*x^67 + 108*x^66 + 17*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 73*x^27 + 108*x^26 + 63*x^25 + 50*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 22*x^20 + 13*x^19 + 116*x^18 + 11*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 119*x^11 + 36*x^10 + 33*x^9 + 126*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 42*x^4 + 11*x^3 + 60*x^2 + 61*x + 30, x^95 + 15*x^93 + 22*x^92 + 117*x^91 + 92*x^90 + 19*x^89 + 2*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 22*x^84 + 73*x^83 + 68*x^82 + 79*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 51*x^75 + 84*x^74 + 37*x^73 + 126*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 26*x^68 + 55*x^67 + 76*x^66 + 81*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 41*x^27 + 12*x^26 + 127*x^25 + 10*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 46*x^20 + 45*x^19 + 20*x^18 + 75*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 23*x^11 + 4*x^10 + 97*x^9 + 38*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 82*x^4 + 107*x^3 + 28*x^2 + 125*x + 102, x^95 + 15*x^93 + 90*x^92 + 5*x^91 + 116*x^90 + 3*x^89 + 30*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 58*x^84 + 121*x^83 + 44*x^82 + 31*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 99*x^75 + 28*x^74 + 117*x^73 + 34*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 86*x^68 + 71*x^67 + 4*x^66 + 65*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 121*x^27 + 4*x^26 + 47*x^25 + 22*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 98*x^20 + 29*x^19 + 28*x^18 + 91*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 7*x^11 + 44*x^10 + 113*x^9 + 122*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 94*x^4 + 59*x^3 + 116*x^2 + 45*x + 26, x^95 + 15*x^93 + 54*x^92 + 5*x^91 + 108*x^90 + 3*x^89 + 82*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 86*x^84 + 121*x^83 + 116*x^82 + 31*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 99*x^75 + 4*x^74 + 117*x^73 + 110*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 26*x^68 + 71*x^67 + 92*x^66 + 65*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 121*x^27 + 92*x^26 + 47*x^25 + 26*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 110*x^20 + 29*x^19 + 4*x^18 + 91*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 7*x^11 + 116*x^10 + 113*x^9 + 86*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 82*x^4 + 59*x^3 + 108*x^2 + 45*x + 54, x^95 + 15*x^93 + 126*x^92 + 37*x^91 + 44*x^90 + 67*x^89 + 90*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 62*x^84 + 89*x^83 + 116*x^82 + 95*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 67*x^75 + 68*x^74 + 53*x^73 + 38*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 50*x^68 + 103*x^67 + 92*x^66 + x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 25*x^27 + 28*x^26 + 111*x^25 + 66*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 118*x^20 + 125*x^19 + 4*x^18 + 27*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 103*x^11 + 52*x^10 + 49*x^9 + 46*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 10*x^4 + 91*x^3 + 108*x^2 + 109*x + 46, x^95 + 15*x^93 + 98*x^92 + 117*x^91 + 100*x^90 + 115*x^89 + 54*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 66*x^84 + 73*x^83 + 60*x^82 + 111*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 51*x^75 + 108*x^74 + 69*x^73 + 10*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 14*x^68 + 55*x^67 + 52*x^66 + 49*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 41*x^27 + 52*x^26 + 95*x^25 + 14*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 10*x^20 + 45*x^19 + 108*x^18 + 107*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 23*x^11 + 60*x^10 + x^9 + 66*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 54*x^4 + 107*x^3 + 100*x^2 + 93*x + 98, x^95 + 15*x^93 + 70*x^92 + 69*x^91 + 76*x^90 + 67*x^89 + 66*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 102*x^84 + 57*x^83 + 20*x^82 + 95*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 35*x^75 + 36*x^74 + 53*x^73 + 126*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 10*x^68 + 7*x^67 + 60*x^66 + x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 57*x^27 + 60*x^26 + 111*x^25 + 74*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 62*x^20 + 93*x^19 + 36*x^18 + 27*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 71*x^11 + 20*x^10 + 49*x^9 + 38*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 2*x^4 + 123*x^3 + 76*x^2 + 109*x + 6, x^95 + 15*x^93 + 74*x^92 + 101*x^91 + 52*x^90 + 35*x^89 + 14*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 106*x^84 + 25*x^83 + 108*x^82 + 127*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 3*x^75 + 92*x^74 + 85*x^73 + 50*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 38*x^68 + 39*x^67 + 68*x^66 + 97*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 89*x^27 + 68*x^26 + 79*x^25 + 70*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 82*x^20 + 61*x^19 + 92*x^18 + 59*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 39*x^11 + 108*x^10 + 81*x^9 + 74*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 110*x^4 + 27*x^3 + 52*x^2 + 77*x + 42, x^95 + 15*x^93 + 2*x^92 + 69*x^91 + 116*x^90 + 99*x^89 + 70*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 2*x^84 + 57*x^83 + 108*x^82 + 63*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 35*x^75 + 28*x^74 + 21*x^73 + 58*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 14*x^68 + 7*x^67 + 68*x^66 + 33*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 57*x^27 + 4*x^26 + 15*x^25 + 94*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 74*x^20 + 93*x^19 + 92*x^18 + 123*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 71*x^11 + 44*x^10 + 17*x^9 + 50*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 54*x^4 + 123*x^3 + 52*x^2 + 13*x + 114, x^95 + 15*x^93 + 110*x^92 + 85*x^91 + 124*x^90 + 83*x^89 + 58*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 14*x^84 + 105*x^83 + 100*x^82 + 15*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 83*x^75 + 52*x^74 + 101*x^73 + 6*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 34*x^68 + 23*x^67 + 44*x^66 + 17*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 9*x^27 + 44*x^26 + 63*x^25 + 34*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 6*x^20 + 77*x^19 + 52*x^18 + 11*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 55*x^11 + 100*x^10 + 33*x^9 + 14*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 58*x^4 + 75*x^3 + 124*x^2 + 61*x + 110, x^95 + 15*x^93 + 118*x^92 + 101*x^91 + 108*x^90 + 35*x^89 + 18*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 22*x^84 + 25*x^83 + 116*x^82 + 127*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 3*x^75 + 4*x^74 + 85*x^73 + 46*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 90*x^68 + 39*x^67 + 92*x^66 + 97*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 89*x^27 + 92*x^26 + 79*x^25 + 90*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 46*x^20 + 61*x^19 + 4*x^18 + 59*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 39*x^11 + 116*x^10 + 81*x^9 + 22*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 18*x^4 + 27*x^3 + 108*x^2 + 77*x + 118, x^95 + 15*x^93 + 122*x^92 + 53*x^91 + 68*x^90 + 83*x^89 + 46*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 122*x^84 + 9*x^83 + 28*x^82 + 15*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 115*x^75 + 12*x^74 + 101*x^73 + 82*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 86*x^68 + 119*x^67 + 84*x^66 + 17*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 105*x^27 + 20*x^26 + 63*x^25 + 102*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 34*x^20 + 109*x^19 + 76*x^18 + 11*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 87*x^11 + 92*x^10 + 33*x^9 + 106*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 94*x^4 + 43*x^3 + 4*x^2 + 61*x + 42, x^95 + 15*x^93 + 70*x^92 + 37*x^91 + 76*x^90 + 99*x^89 + 66*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 102*x^84 + 89*x^83 + 20*x^82 + 63*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 67*x^75 + 36*x^74 + 21*x^73 + 126*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 10*x^68 + 103*x^67 + 60*x^66 + 33*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 25*x^27 + 60*x^26 + 15*x^25 + 74*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 62*x^20 + 125*x^19 + 36*x^18 + 123*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 103*x^11 + 20*x^10 + 17*x^9 + 38*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 2*x^4 + 91*x^3 + 76*x^2 + 13*x + 6, x^95 + 15*x^93 + 122*x^92 + 21*x^91 + 68*x^90 + 51*x^89 + 110*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 122*x^84 + 41*x^83 + 28*x^82 + 47*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 19*x^75 + 12*x^74 + 5*x^73 + 18*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 86*x^68 + 87*x^67 + 84*x^66 + 113*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 73*x^27 + 20*x^26 + 31*x^25 + 38*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 34*x^20 + 13*x^19 + 76*x^18 + 43*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 119*x^11 + 92*x^10 + 65*x^9 + 42*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 94*x^4 + 11*x^3 + 4*x^2 + 29*x + 106, x^95 + 15*x^93 + 66*x^92 + 69*x^91 + 84*x^90 + 99*x^89 + 38*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 2*x^84 + 57*x^83 + 12*x^82 + 63*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 35*x^75 + 60*x^74 + 21*x^73 + 90*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 14*x^68 + 7*x^67 + 36*x^66 + 33*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 57*x^27 + 100*x^26 + 15*x^25 + 62*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 74*x^20 + 93*x^19 + 124*x^18 + 123*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 71*x^11 + 76*x^10 + 17*x^9 + 82*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 54*x^4 + 123*x^3 + 20*x^2 + 13*x + 82, x^95 + 15*x^93 + 90*x^92 + 69*x^91 + 116*x^90 + 3*x^89 + 94*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 58*x^84 + 57*x^83 + 44*x^82 + 31*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 35*x^75 + 28*x^74 + 117*x^73 + 98*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 86*x^68 + 7*x^67 + 4*x^66 + 65*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 57*x^27 + 4*x^26 + 47*x^25 + 86*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 98*x^20 + 93*x^19 + 28*x^18 + 91*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 71*x^11 + 44*x^10 + 113*x^9 + 58*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 94*x^4 + 123*x^3 + 116*x^2 + 45*x + 90, x^95 + 15*x^93 + 78*x^92 + 117*x^91 + 92*x^90 + 115*x^89 + 122*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 46*x^84 + 73*x^83 + 4*x^82 + 111*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 51*x^75 + 84*x^74 + 69*x^73 + 70*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 2*x^68 + 55*x^67 + 12*x^66 + 49*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 41*x^27 + 12*x^26 + 95*x^25 + 98*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 38*x^20 + 45*x^19 + 84*x^18 + 107*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 23*x^11 + 4*x^10 + x^9 + 78*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 26*x^4 + 107*x^3 + 92*x^2 + 93*x + 110, x^95 + 15*x^93 + 86*x^92 + 37*x^91 + 44*x^90 + 35*x^89 + 114*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 118*x^84 + 89*x^83 + 52*x^82 + 127*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 67*x^75 + 68*x^74 + 85*x^73 + 78*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 122*x^68 + 103*x^67 + 28*x^66 + 97*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 25*x^27 + 28*x^26 + 79*x^25 + 58*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 14*x^20 + 125*x^19 + 68*x^18 + 59*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 103*x^11 + 52*x^10 + 81*x^9 + 54*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 50*x^4 + 91*x^3 + 44*x^2 + 77*x + 22, x^95 + 15*x^93 + 14*x^92 + 101*x^91 + 44*x^90 + 67*x^89 + 106*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 14*x^84 + 25*x^83 + 116*x^82 + 95*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 3*x^75 + 68*x^74 + 53*x^73 + 22*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 98*x^68 + 39*x^67 + 92*x^66 + x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 89*x^27 + 28*x^26 + 111*x^25 + 18*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 6*x^20 + 61*x^19 + 4*x^18 + 27*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 39*x^11 + 52*x^10 + 49*x^9 + 94*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 122*x^4 + 27*x^3 + 108*x^2 + 109*x + 30, x^95 + 15*x^93 + 46*x^92 + 69*x^91 + 108*x^90 + 99*x^89 + 74*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 46*x^84 + 57*x^83 + 52*x^82 + 63*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 35*x^75 + 4*x^74 + 21*x^73 + 54*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 66*x^68 + 7*x^67 + 28*x^66 + 33*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 57*x^27 + 92*x^26 + 15*x^25 + 114*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 38*x^20 + 93*x^19 + 68*x^18 + 123*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 71*x^11 + 116*x^10 + 17*x^9 + 126*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 90*x^4 + 123*x^3 + 44*x^2 + 13*x + 62, x^95 + 15*x^93 + 66*x^92 + 53*x^91 + 36*x^90 + 51*x^89 + 86*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 34*x^84 + 9*x^83 + 124*x^82 + 47*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 115*x^75 + 44*x^74 + 5*x^73 + 106*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 46*x^68 + 119*x^67 + 116*x^66 + 113*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 105*x^27 + 116*x^26 + 31*x^25 + 46*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 106*x^20 + 109*x^19 + 44*x^18 + 43*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 87*x^11 + 124*x^10 + 65*x^9 + 34*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 86*x^4 + 43*x^3 + 36*x^2 + 29*x + 66, x^95 + 15*x^93 + 38*x^92 + 21*x^91 + 92*x^90 + 51*x^89 + 18*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 102*x^84 + 41*x^83 + 68*x^82 + 47*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 19*x^75 + 84*x^74 + 5*x^73 + 110*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 74*x^68 + 87*x^67 + 76*x^66 + 113*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 73*x^27 + 12*x^26 + 31*x^25 + 90*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 62*x^20 + 13*x^19 + 20*x^18 + 43*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 119*x^11 + 4*x^10 + 65*x^9 + 86*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 66*x^4 + 11*x^3 + 28*x^2 + 29*x + 86, x^95 + 15*x^93 + 82*x^92 + 101*x^91 + 52*x^90 + 3*x^89 + 86*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 18*x^84 + 25*x^83 + 44*x^82 + 31*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 3*x^75 + 92*x^74 + 117*x^73 + 42*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 126*x^68 + 39*x^67 + 4*x^66 + 65*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 89*x^27 + 68*x^26 + 47*x^25 + 46*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 26*x^20 + 61*x^19 + 28*x^18 + 91*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 39*x^11 + 108*x^10 + 113*x^9 + 98*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 102*x^4 + 27*x^3 + 116*x^2 + 45*x + 98, x^95 + 15*x^93 + 110*x^92 + 21*x^91 + 28*x^90 + 19*x^89 + 26*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 78*x^84 + 41*x^83 + 68*x^82 + 79*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 19*x^75 + 20*x^74 + 37*x^73 + 38*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 98*x^68 + 87*x^67 + 76*x^66 + 81*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 73*x^27 + 76*x^26 + 127*x^25 + 2*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 70*x^20 + 13*x^19 + 20*x^18 + 75*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 119*x^11 + 68*x^10 + 97*x^9 + 46*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 122*x^4 + 11*x^3 + 28*x^2 + 125*x + 78, x^95 + 15*x^93 + 34*x^92 + 53*x^91 + 100*x^90 + 51*x^89 + 118*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 2*x^84 + 9*x^83 + 60*x^82 + 47*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 115*x^75 + 108*x^74 + 5*x^73 + 74*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 78*x^68 + 119*x^67 + 52*x^66 + 113*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 105*x^27 + 52*x^26 + 31*x^25 + 78*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 74*x^20 + 109*x^19 + 108*x^18 + 43*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 87*x^11 + 60*x^10 + 65*x^9 + 2*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 118*x^4 + 43*x^3 + 100*x^2 + 29*x + 34, x^95 + 15*x^93 + 110*x^92 + 69*x^91 + 44*x^90 + 35*x^89 + 10*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 110*x^84 + 57*x^83 + 116*x^82 + 127*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 35*x^75 + 68*x^74 + 85*x^73 + 118*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 2*x^68 + 7*x^67 + 92*x^66 + 97*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 57*x^27 + 28*x^26 + 79*x^25 + 50*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 102*x^20 + 93*x^19 + 4*x^18 + 59*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 71*x^11 + 52*x^10 + 81*x^9 + 62*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 26*x^4 + 123*x^3 + 108*x^2 + 77*x + 126, x^95 + 15*x^93 + 26*x^92 + 101*x^91 + 116*x^90 + 35*x^89 + 94*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 122*x^84 + 25*x^83 + 44*x^82 + 127*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 3*x^75 + 28*x^74 + 85*x^73 + 98*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 22*x^68 + 39*x^67 + 4*x^66 + 97*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 89*x^27 + 4*x^26 + 79*x^25 + 86*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 34*x^20 + 61*x^19 + 28*x^18 + 59*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 39*x^11 + 44*x^10 + 81*x^9 + 58*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 30*x^4 + 27*x^3 + 116*x^2 + 77*x + 90, x^95 + 15*x^93 + 58*x^92 + 85*x^91 + 4*x^90 + 51*x^89 + 46*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 58*x^84 + 105*x^83 + 92*x^82 + 47*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 83*x^75 + 76*x^74 + 5*x^73 + 82*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 22*x^68 + 23*x^67 + 20*x^66 + 113*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 9*x^27 + 84*x^26 + 31*x^25 + 102*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 98*x^20 + 77*x^19 + 12*x^18 + 43*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 55*x^11 + 28*x^10 + 65*x^9 + 106*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 30*x^4 + 75*x^3 + 68*x^2 + 29*x + 42, x^95 + 15*x^93 + 2*x^92 + 69*x^91 + 116*x^90 + 35*x^89 + 6*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 2*x^84 + 57*x^83 + 108*x^82 + 127*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 35*x^75 + 28*x^74 + 85*x^73 + 122*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 14*x^68 + 7*x^67 + 68*x^66 + 97*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 57*x^27 + 4*x^26 + 79*x^25 + 30*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 74*x^20 + 93*x^19 + 92*x^18 + 59*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 71*x^11 + 44*x^10 + 81*x^9 + 114*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 54*x^4 + 123*x^3 + 52*x^2 + 77*x + 50, x^95 + 15*x^93 + 46*x^92 + 21*x^91 + 60*x^90 + 19*x^89 + 58*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 78*x^84 + 41*x^83 + 36*x^82 + 79*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 19*x^75 + 116*x^74 + 37*x^73 + 6*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 98*x^68 + 87*x^67 + 108*x^66 + 81*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 73*x^27 + 108*x^26 + 127*x^25 + 34*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 70*x^20 + 13*x^19 + 116*x^18 + 75*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 119*x^11 + 36*x^10 + 97*x^9 + 14*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 122*x^4 + 11*x^3 + 60*x^2 + 125*x + 110, x^95 + 15*x^93 + 102*x^92 + 85*x^91 + 92*x^90 + 51*x^89 + 18*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 38*x^84 + 105*x^83 + 68*x^82 + 47*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 83*x^75 + 84*x^74 + 5*x^73 + 110*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 10*x^68 + 23*x^67 + 76*x^66 + 113*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 9*x^27 + 12*x^26 + 31*x^25 + 90*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 126*x^20 + 77*x^19 + 20*x^18 + 43*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 55*x^11 + 4*x^10 + 65*x^9 + 86*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 2*x^4 + 75*x^3 + 28*x^2 + 29*x + 86, x^95 + 15*x^93 + 90*x^92 + 117*x^91 + 4*x^90 + 19*x^89 + 78*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 90*x^84 + 73*x^83 + 92*x^82 + 79*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 51*x^75 + 76*x^74 + 37*x^73 + 50*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 118*x^68 + 55*x^67 + 20*x^66 + 81*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 41*x^27 + 84*x^26 + 127*x^25 + 6*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 2*x^20 + 45*x^19 + 12*x^18 + 75*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 23*x^11 + 28*x^10 + 97*x^9 + 74*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 126*x^4 + 107*x^3 + 68*x^2 + 125*x + 10, x^95 + 15*x^93 + 118*x^92 + 5*x^91 + 44*x^90 + 67*x^89 + 18*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 22*x^84 + 121*x^83 + 52*x^82 + 95*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 99*x^75 + 68*x^74 + 53*x^73 + 46*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 90*x^68 + 71*x^67 + 28*x^66 + x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 121*x^27 + 28*x^26 + 111*x^25 + 90*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 46*x^20 + 29*x^19 + 68*x^18 + 27*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 7*x^11 + 52*x^10 + 49*x^9 + 22*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 18*x^4 + 59*x^3 + 44*x^2 + 109*x + 118, x^95 + 15*x^93 + 90*x^92 + 69*x^91 + 116*x^90 + 67*x^89 + 30*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 58*x^84 + 57*x^83 + 44*x^82 + 95*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 35*x^75 + 28*x^74 + 53*x^73 + 34*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 86*x^68 + 7*x^67 + 4*x^66 + x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 57*x^27 + 4*x^26 + 111*x^25 + 22*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 98*x^20 + 93*x^19 + 28*x^18 + 27*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 71*x^11 + 44*x^10 + 49*x^9 + 122*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 94*x^4 + 123*x^3 + 116*x^2 + 109*x + 26, x^95 + 15*x^93 + 78*x^92 + 5*x^91 + 76*x^90 + 99*x^89 + 74*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 14*x^84 + 121*x^83 + 84*x^82 + 63*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 99*x^75 + 36*x^74 + 21*x^73 + 54*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 98*x^68 + 71*x^67 + 124*x^66 + 33*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 121*x^27 + 60*x^26 + 15*x^25 + 114*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 6*x^20 + 29*x^19 + 100*x^18 + 123*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 7*x^11 + 20*x^10 + 17*x^9 + 126*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 122*x^4 + 59*x^3 + 12*x^2 + 13*x + 126, x^95 + 15*x^93 + 54*x^92 + 69*x^91 + 108*x^90 + 67*x^89 + 82*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 86*x^84 + 57*x^83 + 116*x^82 + 95*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 35*x^75 + 4*x^74 + 53*x^73 + 110*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 26*x^68 + 7*x^67 + 92*x^66 + x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 57*x^27 + 92*x^26 + 111*x^25 + 26*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 110*x^20 + 93*x^19 + 4*x^18 + 27*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 71*x^11 + 116*x^10 + 49*x^9 + 86*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 82*x^4 + 123*x^3 + 108*x^2 + 109*x + 54, x^95 + 15*x^93 + 46*x^92 + 85*x^91 + 60*x^90 + 19*x^89 + 122*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 78*x^84 + 105*x^83 + 36*x^82 + 79*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 83*x^75 + 116*x^74 + 37*x^73 + 70*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 98*x^68 + 23*x^67 + 108*x^66 + 81*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 9*x^27 + 108*x^26 + 127*x^25 + 98*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 70*x^20 + 77*x^19 + 116*x^18 + 75*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 55*x^11 + 36*x^10 + 97*x^9 + 78*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 122*x^4 + 75*x^3 + 60*x^2 + 125*x + 46, x^95 + 15*x^93 + 114*x^92 + 101*x^91 + 20*x^90 + 67*x^89 + 86*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 114*x^84 + 25*x^83 + 76*x^82 + 95*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 3*x^75 + 124*x^74 + 53*x^73 + 42*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 30*x^68 + 39*x^67 + 100*x^66 + x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 89*x^27 + 36*x^26 + 111*x^25 + 46*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 122*x^20 + 61*x^19 + 60*x^18 + 27*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 39*x^11 + 12*x^10 + 49*x^9 + 98*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 6*x^4 + 27*x^3 + 84*x^2 + 109*x + 34, x^95 + 15*x^93 + 10*x^92 + 85*x^91 + 100*x^90 + 115*x^89 + 30*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 10*x^84 + 105*x^83 + 124*x^82 + 111*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 83*x^75 + 108*x^74 + 69*x^73 + 98*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 70*x^68 + 23*x^67 + 116*x^66 + 49*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 9*x^27 + 52*x^26 + 95*x^25 + 22*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 114*x^20 + 77*x^19 + 44*x^18 + 107*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 55*x^11 + 60*x^10 + x^9 + 58*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 14*x^4 + 75*x^3 + 36*x^2 + 93*x + 122, x^95 + 15*x^93 + 114*x^92 + 85*x^91 + 4*x^90 + 83*x^89 + 38*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 82*x^84 + 105*x^83 + 28*x^82 + 15*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 83*x^75 + 76*x^74 + 101*x^73 + 26*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 126*x^68 + 23*x^67 + 84*x^66 + 17*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 9*x^27 + 84*x^26 + 63*x^25 + 62*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 90*x^20 + 77*x^19 + 76*x^18 + 11*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 55*x^11 + 28*x^10 + 33*x^9 + 18*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 102*x^4 + 75*x^3 + 4*x^2 + 61*x + 50, x^95 + 15*x^93 + 86*x^92 + 117*x^91 + 92*x^90 + 19*x^89 + 66*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 86*x^84 + 73*x^83 + 68*x^82 + 79*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 51*x^75 + 84*x^74 + 37*x^73 + 62*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 90*x^68 + 55*x^67 + 76*x^66 + 81*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 41*x^27 + 12*x^26 + 127*x^25 + 74*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 110*x^20 + 45*x^19 + 20*x^18 + 75*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 23*x^11 + 4*x^10 + 97*x^9 + 102*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 18*x^4 + 107*x^3 + 28*x^2 + 125*x + 38, x^95 + 15*x^93 + 38*x^92 + 69*x^91 + 108*x^90 + 3*x^89 + 66*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 6*x^84 + 57*x^83 + 116*x^82 + 31*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 35*x^75 + 4*x^74 + 117*x^73 + 126*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 106*x^68 + 7*x^67 + 92*x^66 + 65*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 57*x^27 + 92*x^26 + 47*x^25 + 74*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 94*x^20 + 93*x^19 + 4*x^18 + 91*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 71*x^11 + 116*x^10 + 113*x^9 + 38*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 98*x^4 + 123*x^3 + 108*x^2 + 45*x + 70, x^95 + 15*x^93 + 66*x^92 + 53*x^91 + 100*x^90 + 115*x^89 + 86*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 34*x^84 + 9*x^83 + 60*x^82 + 111*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 115*x^75 + 108*x^74 + 69*x^73 + 106*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 46*x^68 + 119*x^67 + 52*x^66 + 49*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 105*x^27 + 52*x^26 + 95*x^25 + 46*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 106*x^20 + 109*x^19 + 108*x^18 + 107*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 87*x^11 + 60*x^10 + x^9 + 34*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 86*x^4 + 43*x^3 + 100*x^2 + 93*x + 66, x^95 + 15*x^93 + 82*x^92 + 69*x^91 + 20*x^90 + 35*x^89 + 118*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 82*x^84 + 57*x^83 + 76*x^82 + 127*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 35*x^75 + 124*x^74 + 85*x^73 + 10*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 62*x^68 + 7*x^67 + 100*x^66 + 97*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 57*x^27 + 36*x^26 + 79*x^25 + 78*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 90*x^20 + 93*x^19 + 60*x^18 + 59*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 71*x^11 + 12*x^10 + 81*x^9 + 66*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 38*x^4 + 123*x^3 + 84*x^2 + 77*x + 2, x^95 + 15*x^93 + 6*x^92 + 117*x^91 + 92*x^90 + 83*x^89 + 114*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 70*x^84 + 73*x^83 + 68*x^82 + 15*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 51*x^75 + 84*x^74 + 101*x^73 + 14*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 106*x^68 + 55*x^67 + 76*x^66 + 17*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 41*x^27 + 12*x^26 + 63*x^25 + 58*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 30*x^20 + 45*x^19 + 20*x^18 + 11*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 23*x^11 + 4*x^10 + 33*x^9 + 118*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 98*x^4 + 107*x^3 + 28*x^2 + 61*x + 118, x^95 + 15*x^93 + 42*x^92 + 85*x^91 + 68*x^90 + 51*x^89 + 30*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 106*x^84 + 105*x^83 + 28*x^82 + 47*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 83*x^75 + 12*x^74 + 5*x^73 + 98*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 102*x^68 + 23*x^67 + 84*x^66 + 113*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 9*x^27 + 20*x^26 + 31*x^25 + 22*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 82*x^20 + 77*x^19 + 76*x^18 + 43*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 55*x^11 + 92*x^10 + 65*x^9 + 58*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 46*x^4 + 75*x^3 + 4*x^2 + 29*x + 58, x^95 + 15*x^93 + 90*x^92 + 53*x^91 + 36*x^90 + 19*x^89 + 110*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 26*x^84 + 9*x^83 + 60*x^82 + 79*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 115*x^75 + 44*x^74 + 37*x^73 + 18*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 54*x^68 + 119*x^67 + 52*x^66 + 81*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 105*x^27 + 116*x^26 + 127*x^25 + 38*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 66*x^20 + 109*x^19 + 108*x^18 + 75*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 87*x^11 + 124*x^10 + 97*x^9 + 42*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 62*x^4 + 43*x^3 + 100*x^2 + 125*x + 42, x^95 + 15*x^93 + 98*x^92 + 21*x^91 + 36*x^90 + 83*x^89 + 118*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 66*x^84 + 41*x^83 + 124*x^82 + 15*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 19*x^75 + 44*x^74 + 101*x^73 + 74*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 14*x^68 + 87*x^67 + 116*x^66 + 17*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 73*x^27 + 116*x^26 + 63*x^25 + 78*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 10*x^20 + 13*x^19 + 44*x^18 + 11*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 119*x^11 + 124*x^10 + 33*x^9 + 2*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 54*x^4 + 11*x^3 + 36*x^2 + 61*x + 34, x^95 + 15*x^93 + 26*x^92 + 69*x^91 + 84*x^90 + 3*x^89 + 62*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 58*x^84 + 57*x^83 + 76*x^82 + 31*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 35*x^75 + 60*x^74 + 117*x^73 + 2*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 86*x^68 + 7*x^67 + 100*x^66 + 65*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 57*x^27 + 100*x^26 + 47*x^25 + 54*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 98*x^20 + 93*x^19 + 60*x^18 + 91*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 71*x^11 + 76*x^10 + 113*x^9 + 90*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 94*x^4 + 123*x^3 + 84*x^2 + 45*x + 58, x^95 + 15*x^93 + 6*x^92 + 85*x^91 + 60*x^90 + 115*x^89 + 18*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 6*x^84 + 105*x^83 + 100*x^82 + 111*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 83*x^75 + 116*x^74 + 69*x^73 + 110*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 42*x^68 + 23*x^67 + 44*x^66 + 49*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 9*x^27 + 108*x^26 + 95*x^25 + 90*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 94*x^20 + 77*x^19 + 52*x^18 + 107*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 55*x^11 + 36*x^10 + x^9 + 86*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 34*x^4 + 75*x^3 + 124*x^2 + 93*x + 22, x^95 + 15*x^93 + 82*x^92 + 85*x^91 + 36*x^90 + 83*x^89 + 102*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 114*x^84 + 105*x^83 + 124*x^82 + 15*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 83*x^75 + 44*x^74 + 101*x^73 + 90*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 94*x^68 + 23*x^67 + 116*x^66 + 17*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 9*x^27 + 116*x^26 + 63*x^25 + 126*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 122*x^20 + 77*x^19 + 44*x^18 + 11*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 55*x^11 + 124*x^10 + 33*x^9 + 82*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 70*x^4 + 75*x^3 + 36*x^2 + 61*x + 50, x^95 + 15*x^93 + 74*x^92 + 21*x^91 + 68*x^90 + 51*x^89 + 126*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 10*x^84 + 41*x^83 + 28*x^82 + 47*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 19*x^75 + 12*x^74 + 5*x^73 + 2*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 70*x^68 + 87*x^67 + 84*x^66 + 113*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 73*x^27 + 20*x^26 + 31*x^25 + 118*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 114*x^20 + 13*x^19 + 76*x^18 + 43*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 119*x^11 + 92*x^10 + 65*x^9 + 90*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 14*x^4 + 11*x^3 + 4*x^2 + 29*x + 90, x^95 + 15*x^93 + 70*x^92 + 5*x^91 + 76*x^90 + 3*x^89 + 66*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 102*x^84 + 121*x^83 + 20*x^82 + 31*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 99*x^75 + 36*x^74 + 117*x^73 + 126*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 10*x^68 + 71*x^67 + 60*x^66 + 65*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 121*x^27 + 60*x^26 + 47*x^25 + 74*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 62*x^20 + 29*x^19 + 36*x^18 + 91*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 7*x^11 + 20*x^10 + 113*x^9 + 38*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 2*x^4 + 59*x^3 + 76*x^2 + 45*x + 6, x^95 + 15*x^93 + 18*x^92 + 117*x^91 + 68*x^90 + 115*x^89 + 70*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 114*x^84 + 73*x^83 + 92*x^82 + 111*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 51*x^75 + 12*x^74 + 69*x^73 + 122*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 94*x^68 + 55*x^67 + 20*x^66 + 49*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 41*x^27 + 20*x^26 + 95*x^25 + 94*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 122*x^20 + 45*x^19 + 12*x^18 + 107*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 23*x^11 + 92*x^10 + x^9 + 114*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 70*x^4 + 107*x^3 + 68*x^2 + 93*x + 18, x^95 + 15*x^93 + 102*x^92 + 101*x^91 + 12*x^90 + 35*x^89 + 34*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 6*x^84 + 25*x^83 + 84*x^82 + 127*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 3*x^75 + 100*x^74 + 85*x^73 + 30*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 106*x^68 + 39*x^67 + 124*x^66 + 97*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 89*x^27 + 124*x^26 + 79*x^25 + 42*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 94*x^20 + 61*x^19 + 100*x^18 + 59*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 39*x^11 + 84*x^10 + 81*x^9 + 70*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 98*x^4 + 27*x^3 + 12*x^2 + 77*x + 38, x^95 + 15*x^93 + 14*x^92 + 69*x^91 + 76*x^90 + 99*x^89 + 74*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 78*x^84 + 57*x^83 + 84*x^82 + 63*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 35*x^75 + 36*x^74 + 21*x^73 + 54*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 34*x^68 + 7*x^67 + 124*x^66 + 33*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 57*x^27 + 60*x^26 + 15*x^25 + 114*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 70*x^20 + 93*x^19 + 100*x^18 + 123*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 71*x^11 + 20*x^10 + 17*x^9 + 126*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 58*x^4 + 123*x^3 + 12*x^2 + 13*x + 126, x^95 + 15*x^93 + 110*x^92 + 69*x^91 + 12*x^90 + 35*x^89 + 42*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 46*x^84 + 57*x^83 + 20*x^82 + 127*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 35*x^75 + 100*x^74 + 85*x^73 + 86*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 66*x^68 + 7*x^67 + 60*x^66 + 97*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 57*x^27 + 124*x^26 + 79*x^25 + 82*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 38*x^20 + 93*x^19 + 36*x^18 + 59*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 71*x^11 + 84*x^10 + 81*x^9 + 30*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 90*x^4 + 123*x^3 + 76*x^2 + 77*x + 30, x^95 + 15*x^93 + 2*x^92 + 21*x^91 + 68*x^90 + 83*x^89 + 118*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 34*x^84 + 41*x^83 + 92*x^82 + 15*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 19*x^75 + 12*x^74 + 101*x^73 + 74*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 46*x^68 + 87*x^67 + 20*x^66 + 17*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 73*x^27 + 20*x^26 + 63*x^25 + 78*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 106*x^20 + 13*x^19 + 12*x^18 + 11*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 119*x^11 + 92*x^10 + 33*x^9 + 2*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 86*x^4 + 11*x^3 + 68*x^2 + 61*x + 98, x^95 + 15*x^93 + 90*x^92 + 85*x^91 + 68*x^90 + 115*x^89 + 78*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 90*x^84 + 105*x^83 + 28*x^82 + 111*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 83*x^75 + 12*x^74 + 69*x^73 + 50*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 118*x^68 + 23*x^67 + 84*x^66 + 49*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 9*x^27 + 20*x^26 + 95*x^25 + 6*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 2*x^20 + 77*x^19 + 76*x^18 + 107*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 55*x^11 + 92*x^10 + x^9 + 74*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 126*x^4 + 75*x^3 + 4*x^2 + 93*x + 10, x^95 + 15*x^93 + 118*x^92 + 117*x^91 + 124*x^90 + 83*x^89 + 2*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 54*x^84 + 73*x^83 + 36*x^82 + 15*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 51*x^75 + 52*x^74 + 101*x^73 + 126*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 122*x^68 + 55*x^67 + 108*x^66 + 17*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 41*x^27 + 44*x^26 + 63*x^25 + 10*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 78*x^20 + 45*x^19 + 116*x^18 + 11*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 23*x^11 + 100*x^10 + 33*x^9 + 38*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 50*x^4 + 107*x^3 + 60*x^2 + 61*x + 38, x^95 + 15*x^93 + 26*x^92 + 117*x^91 + 4*x^90 + 19*x^89 + 14*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 26*x^84 + 73*x^83 + 92*x^82 + 79*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 51*x^75 + 76*x^74 + 37*x^73 + 114*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 54*x^68 + 55*x^67 + 20*x^66 + 81*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 41*x^27 + 84*x^26 + 127*x^25 + 70*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 66*x^20 + 45*x^19 + 12*x^18 + 75*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 23*x^11 + 28*x^10 + 97*x^9 + 10*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 62*x^4 + 107*x^3 + 68*x^2 + 125*x + 74, x^95 + 15*x^93 + 86*x^92 + 37*x^91 + 108*x^90 + 35*x^89 + 50*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 118*x^84 + 89*x^83 + 116*x^82 + 127*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 67*x^75 + 4*x^74 + 85*x^73 + 14*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 122*x^68 + 103*x^67 + 92*x^66 + 97*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 25*x^27 + 92*x^26 + 79*x^25 + 122*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 14*x^20 + 125*x^19 + 4*x^18 + 59*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 103*x^11 + 116*x^10 + 81*x^9 + 118*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 50*x^4 + 91*x^3 + 108*x^2 + 77*x + 86, x^95 + 15*x^93 + 62*x^92 + 69*x^91 + 44*x^90 + 99*x^89 + 90*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 126*x^84 + 57*x^83 + 116*x^82 + 63*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 35*x^75 + 68*x^74 + 21*x^73 + 38*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 114*x^68 + 7*x^67 + 92*x^66 + 33*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 57*x^27 + 28*x^26 + 15*x^25 + 66*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 54*x^20 + 93*x^19 + 4*x^18 + 123*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 71*x^11 + 52*x^10 + 17*x^9 + 46*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 74*x^4 + 123*x^3 + 108*x^2 + 13*x + 46, x^95 + 15*x^93 + 114*x^92 + 21*x^91 + 4*x^90 + 19*x^89 + 38*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 82*x^84 + 41*x^83 + 28*x^82 + 79*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 19*x^75 + 76*x^74 + 37*x^73 + 26*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 126*x^68 + 87*x^67 + 84*x^66 + 81*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 73*x^27 + 84*x^26 + 127*x^25 + 62*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 90*x^20 + 13*x^19 + 76*x^18 + 75*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 119*x^11 + 28*x^10 + 97*x^9 + 18*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 102*x^4 + 11*x^3 + 4*x^2 + 125*x + 50, x^95 + 15*x^93 + 18*x^92 + 37*x^91 + 116*x^90 + 3*x^89 + 22*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 82*x^84 + 89*x^83 + 108*x^82 + 31*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 67*x^75 + 28*x^74 + 117*x^73 + 106*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 62*x^68 + 103*x^67 + 68*x^66 + 65*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 25*x^27 + 4*x^26 + 47*x^25 + 110*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 90*x^20 + 125*x^19 + 92*x^18 + 91*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 103*x^11 + 44*x^10 + 113*x^9 + 34*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 38*x^4 + 91*x^3 + 52*x^2 + 45*x + 34, x^95 + 15*x^93 + 86*x^92 + 101*x^91 + 44*x^90 + 35*x^89 + 50*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 118*x^84 + 25*x^83 + 52*x^82 + 127*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 3*x^75 + 68*x^74 + 85*x^73 + 14*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 122*x^68 + 39*x^67 + 28*x^66 + 97*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 89*x^27 + 28*x^26 + 79*x^25 + 122*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 14*x^20 + 61*x^19 + 68*x^18 + 59*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 39*x^11 + 52*x^10 + 81*x^9 + 118*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 50*x^4 + 27*x^3 + 44*x^2 + 77*x + 86, x^95 + 15*x^93 + 14*x^92 + 53*x^91 + 92*x^90 + 51*x^89 + 58*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 110*x^84 + 9*x^83 + 4*x^82 + 47*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 115*x^75 + 84*x^74 + 5*x^73 + 6*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 66*x^68 + 119*x^67 + 12*x^66 + 113*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 105*x^27 + 12*x^26 + 31*x^25 + 34*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 102*x^20 + 109*x^19 + 84*x^18 + 43*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 87*x^11 + 4*x^10 + 65*x^9 + 14*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 90*x^4 + 43*x^3 + 92*x^2 + 29*x + 46, x^95 + 15*x^93 + 70*x^92 + 69*x^91 + 108*x^90 + 67*x^89 + 34*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 38*x^84 + 57*x^83 + 116*x^82 + 95*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 35*x^75 + 4*x^74 + 53*x^73 + 30*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 74*x^68 + 7*x^67 + 92*x^66 + x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 57*x^27 + 92*x^26 + 111*x^25 + 42*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 126*x^20 + 93*x^19 + 4*x^18 + 27*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 71*x^11 + 116*x^10 + 49*x^9 + 70*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 66*x^4 + 123*x^3 + 108*x^2 + 109*x + 102, x^95 + 15*x^93 + 14*x^92 + 37*x^91 + 12*x^90 + 3*x^89 + 10*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 78*x^84 + 89*x^83 + 20*x^82 + 31*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 67*x^75 + 100*x^74 + 117*x^73 + 118*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 34*x^68 + 103*x^67 + 60*x^66 + 65*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 25*x^27 + 124*x^26 + 47*x^25 + 50*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 70*x^20 + 125*x^19 + 36*x^18 + 91*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 103*x^11 + 84*x^10 + 113*x^9 + 62*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 58*x^4 + 91*x^3 + 76*x^2 + 45*x + 62, x^95 + 15*x^93 + 106*x^92 + 5*x^91 + 20*x^90 + 3*x^89 + 78*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 74*x^84 + 121*x^83 + 12*x^82 + 31*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 99*x^75 + 124*x^74 + 117*x^73 + 114*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 70*x^68 + 71*x^67 + 36*x^66 + 65*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 121*x^27 + 36*x^26 + 47*x^25 + 6*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 50*x^20 + 29*x^19 + 124*x^18 + 91*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 7*x^11 + 12*x^10 + 113*x^9 + 10*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 14*x^4 + 59*x^3 + 20*x^2 + 45*x + 42, x^95 + 15*x^93 + 106*x^92 + 85*x^91 + 4*x^90 + 115*x^89 + 94*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 42*x^84 + 105*x^83 + 92*x^82 + 111*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 83*x^75 + 76*x^74 + 69*x^73 + 34*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 38*x^68 + 23*x^67 + 20*x^66 + 49*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 9*x^27 + 84*x^26 + 95*x^25 + 86*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 18*x^20 + 77*x^19 + 12*x^18 + 107*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 55*x^11 + 28*x^10 + x^9 + 122*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 110*x^4 + 75*x^3 + 68*x^2 + 93*x + 122, x^95 + 15*x^93 + 98*x^92 + 53*x^91 + 36*x^90 + 115*x^89 + 54*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 66*x^84 + 9*x^83 + 124*x^82 + 111*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 115*x^75 + 44*x^74 + 69*x^73 + 10*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 14*x^68 + 119*x^67 + 116*x^66 + 49*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 105*x^27 + 116*x^26 + 95*x^25 + 14*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 10*x^20 + 109*x^19 + 44*x^18 + 107*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 87*x^11 + 124*x^10 + x^9 + 66*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 54*x^4 + 43*x^3 + 36*x^2 + 93*x + 98, x^95 + 15*x^93 + 70*x^92 + 85*x^91 + 124*x^90 + 51*x^89 + 82*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 70*x^84 + 105*x^83 + 36*x^82 + 47*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 83*x^75 + 52*x^74 + 5*x^73 + 46*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 106*x^68 + 23*x^67 + 108*x^66 + 113*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 9*x^27 + 44*x^26 + 31*x^25 + 26*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 30*x^20 + 77*x^19 + 116*x^18 + 43*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 55*x^11 + 100*x^10 + 65*x^9 + 22*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 98*x^4 + 75*x^3 + 60*x^2 + 29*x + 86, x^95 + 15*x^93 + 90*x^92 + 21*x^91 + 4*x^90 + 115*x^89 + 78*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 90*x^84 + 41*x^83 + 92*x^82 + 111*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 19*x^75 + 76*x^74 + 69*x^73 + 50*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 118*x^68 + 87*x^67 + 20*x^66 + 49*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 73*x^27 + 84*x^26 + 95*x^25 + 6*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 2*x^20 + 13*x^19 + 12*x^18 + 107*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 119*x^11 + 28*x^10 + x^9 + 74*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 126*x^4 + 11*x^3 + 68*x^2 + 93*x + 10, x^95 + 15*x^93 + 26*x^92 + 117*x^91 + 100*x^90 + 19*x^89 + 46*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 90*x^84 + 73*x^83 + 124*x^82 + 79*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 51*x^75 + 108*x^74 + 37*x^73 + 82*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 118*x^68 + 55*x^67 + 116*x^66 + 81*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 41*x^27 + 52*x^26 + 127*x^25 + 102*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 2*x^20 + 45*x^19 + 44*x^18 + 75*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 23*x^11 + 60*x^10 + 97*x^9 + 106*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 126*x^4 + 107*x^3 + 36*x^2 + 125*x + 106, x^95 + 15*x^93 + 126*x^92 + 101*x^91 + 108*x^90 + 67*x^89 + 90*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 62*x^84 + 25*x^83 + 52*x^82 + 95*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 3*x^75 + 4*x^74 + 53*x^73 + 38*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 50*x^68 + 39*x^67 + 28*x^66 + x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 89*x^27 + 92*x^26 + 111*x^25 + 66*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 118*x^20 + 61*x^19 + 68*x^18 + 27*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 39*x^11 + 116*x^10 + 49*x^9 + 46*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 10*x^4 + 27*x^3 + 44*x^2 + 109*x + 46, x^95 + 15*x^93 + 46*x^92 + 5*x^91 + 108*x^90 + 99*x^89 + 10*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 46*x^84 + 121*x^83 + 52*x^82 + 63*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 99*x^75 + 4*x^74 + 21*x^73 + 118*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 66*x^68 + 71*x^67 + 28*x^66 + 33*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 121*x^27 + 92*x^26 + 15*x^25 + 50*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 38*x^20 + 29*x^19 + 68*x^18 + 123*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 7*x^11 + 116*x^10 + 17*x^9 + 62*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 90*x^4 + 59*x^3 + 44*x^2 + 13*x + 126, x^95 + 15*x^93 + 54*x^92 + 53*x^91 + 60*x^90 + 83*x^89 + 66*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 118*x^84 + 9*x^83 + 100*x^82 + 15*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 115*x^75 + 116*x^74 + 101*x^73 + 62*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 58*x^68 + 119*x^67 + 44*x^66 + 17*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 105*x^27 + 108*x^26 + 63*x^25 + 74*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 14*x^20 + 109*x^19 + 52*x^18 + 11*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 87*x^11 + 36*x^10 + 33*x^9 + 102*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 114*x^4 + 43*x^3 + 124*x^2 + 61*x + 102, x^95 + 15*x^93 + 86*x^92 + 85*x^91 + 28*x^90 + 51*x^89 + 2*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 86*x^84 + 105*x^83 + 4*x^82 + 47*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 83*x^75 + 20*x^74 + 5*x^73 + 126*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 90*x^68 + 23*x^67 + 12*x^66 + 113*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 9*x^27 + 76*x^26 + 31*x^25 + 10*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 110*x^20 + 77*x^19 + 84*x^18 + 43*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 55*x^11 + 68*x^10 + 65*x^9 + 38*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 18*x^4 + 75*x^3 + 92*x^2 + 29*x + 102, x^95 + 15*x^93 + 10*x^92 + 53*x^91 + 36*x^90 + 83*x^89 + 30*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 10*x^84 + 9*x^83 + 60*x^82 + 15*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 115*x^75 + 44*x^74 + 101*x^73 + 98*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 70*x^68 + 119*x^67 + 52*x^66 + 17*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 105*x^27 + 116*x^26 + 63*x^25 + 22*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 114*x^20 + 109*x^19 + 108*x^18 + 11*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 87*x^11 + 124*x^10 + 33*x^9 + 58*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 14*x^4 + 43*x^3 + 100*x^2 + 61*x + 122, x^95 + 15*x^93 + 10*x^92 + 85*x^91 + 4*x^90 + 115*x^89 + 126*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 74*x^84 + 105*x^83 + 92*x^82 + 111*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 83*x^75 + 76*x^74 + 69*x^73 + 2*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 6*x^68 + 23*x^67 + 20*x^66 + 49*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 9*x^27 + 84*x^26 + 95*x^25 + 118*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 50*x^20 + 77*x^19 + 12*x^18 + 107*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 55*x^11 + 28*x^10 + x^9 + 90*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 78*x^4 + 75*x^3 + 68*x^2 + 93*x + 90, x^95 + 15*x^93 + 14*x^92 + 101*x^91 + 12*x^90 + 67*x^89 + 10*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 78*x^84 + 25*x^83 + 20*x^82 + 95*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 3*x^75 + 100*x^74 + 53*x^73 + 118*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 34*x^68 + 39*x^67 + 60*x^66 + x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 89*x^27 + 124*x^26 + 111*x^25 + 50*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 70*x^20 + 61*x^19 + 36*x^18 + 27*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 39*x^11 + 84*x^10 + 49*x^9 + 62*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 58*x^4 + 27*x^3 + 76*x^2 + 109*x + 62, x^95 + 15*x^93 + 114*x^92 + 117*x^91 + 4*x^90 + 115*x^89 + 102*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 82*x^84 + 73*x^83 + 28*x^82 + 111*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 51*x^75 + 76*x^74 + 69*x^73 + 90*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 126*x^68 + 55*x^67 + 84*x^66 + 49*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 41*x^27 + 84*x^26 + 95*x^25 + 126*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 90*x^20 + 45*x^19 + 76*x^18 + 107*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 23*x^11 + 28*x^10 + x^9 + 82*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 102*x^4 + 107*x^3 + 4*x^2 + 93*x + 114, x^95 + 15*x^93 + 2*x^92 + 117*x^91 + 36*x^90 + 115*x^89 + 22*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 98*x^84 + 73*x^83 + 124*x^82 + 111*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 51*x^75 + 44*x^74 + 69*x^73 + 42*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 110*x^68 + 55*x^67 + 116*x^66 + 49*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 41*x^27 + 116*x^26 + 95*x^25 + 110*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 42*x^20 + 45*x^19 + 44*x^18 + 107*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 23*x^11 + 124*x^10 + x^9 + 98*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 22*x^4 + 107*x^3 + 36*x^2 + 93*x + 2, x^95 + 15*x^93 + 106*x^92 + 5*x^91 + 84*x^90 + 3*x^89 + 14*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 74*x^84 + 121*x^83 + 76*x^82 + 31*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 99*x^75 + 60*x^74 + 117*x^73 + 50*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 70*x^68 + 71*x^67 + 100*x^66 + 65*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 121*x^27 + 100*x^26 + 47*x^25 + 70*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 50*x^20 + 29*x^19 + 60*x^18 + 91*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 7*x^11 + 76*x^10 + 113*x^9 + 74*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 14*x^4 + 59*x^3 + 84*x^2 + 45*x + 106, x^95 + 15*x^93 + 114*x^92 + 5*x^91 + 52*x^90 + 35*x^89 + 54*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 50*x^84 + 121*x^83 + 44*x^82 + 127*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 99*x^75 + 92*x^74 + 85*x^73 + 74*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 94*x^68 + 71*x^67 + 4*x^66 + 97*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 121*x^27 + 68*x^26 + 79*x^25 + 14*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 58*x^20 + 29*x^19 + 28*x^18 + 59*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 7*x^11 + 108*x^10 + 81*x^9 + 2*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 70*x^4 + 59*x^3 + 116*x^2 + 77*x + 2, x^95 + 15*x^93 + 66*x^92 + 53*x^91 + 68*x^90 + 115*x^89 + 118*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 98*x^84 + 9*x^83 + 92*x^82 + 111*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 115*x^75 + 12*x^74 + 69*x^73 + 74*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 110*x^68 + 119*x^67 + 20*x^66 + 49*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 105*x^27 + 20*x^26 + 95*x^25 + 78*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 42*x^20 + 109*x^19 + 12*x^18 + 107*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 87*x^11 + 92*x^10 + x^9 + 2*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 22*x^4 + 43*x^3 + 68*x^2 + 93*x + 98, x^95 + 15*x^93 + 110*x^92 + 85*x^91 + 60*x^90 + 19*x^89 + 58*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 14*x^84 + 105*x^83 + 36*x^82 + 79*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 83*x^75 + 116*x^74 + 37*x^73 + 6*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 34*x^68 + 23*x^67 + 108*x^66 + 81*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 9*x^27 + 108*x^26 + 127*x^25 + 34*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 6*x^20 + 77*x^19 + 116*x^18 + 75*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 55*x^11 + 36*x^10 + 97*x^9 + 14*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 58*x^4 + 75*x^3 + 60*x^2 + 125*x + 110, x^95 + 15*x^93 + 34*x^92 + 69*x^91 + 84*x^90 + 99*x^89 + 6*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 98*x^84 + 57*x^83 + 12*x^82 + 63*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 35*x^75 + 60*x^74 + 21*x^73 + 122*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 46*x^68 + 7*x^67 + 36*x^66 + 33*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 57*x^27 + 100*x^26 + 15*x^25 + 30*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 42*x^20 + 93*x^19 + 124*x^18 + 123*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 71*x^11 + 76*x^10 + 17*x^9 + 114*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 86*x^4 + 123*x^3 + 20*x^2 + 13*x + 114, x^95 + 15*x^93 + 118*x^92 + 5*x^91 + 12*x^90 + 3*x^89 + 114*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 86*x^84 + 121*x^83 + 84*x^82 + 31*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 99*x^75 + 100*x^74 + 117*x^73 + 78*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 26*x^68 + 71*x^67 + 124*x^66 + 65*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 121*x^27 + 124*x^26 + 47*x^25 + 58*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 110*x^20 + 29*x^19 + 100*x^18 + 91*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 7*x^11 + 84*x^10 + 113*x^9 + 54*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 82*x^4 + 59*x^3 + 12*x^2 + 45*x + 86, x^95 + 15*x^93 + 42*x^92 + 85*x^91 + 4*x^90 + 51*x^89 + 94*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 106*x^84 + 105*x^83 + 92*x^82 + 47*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 83*x^75 + 76*x^74 + 5*x^73 + 34*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 102*x^68 + 23*x^67 + 20*x^66 + 113*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 9*x^27 + 84*x^26 + 31*x^25 + 86*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 82*x^20 + 77*x^19 + 12*x^18 + 43*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 55*x^11 + 28*x^10 + 65*x^9 + 122*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 46*x^4 + 75*x^3 + 68*x^2 + 29*x + 122, x^95 + 15*x^93 + 126*x^92 + 21*x^91 + 124*x^90 + 83*x^89 + 74*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 94*x^84 + 41*x^83 + 100*x^82 + 15*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 19*x^75 + 52*x^74 + 101*x^73 + 118*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 82*x^68 + 87*x^67 + 44*x^66 + 17*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 73*x^27 + 44*x^26 + 63*x^25 + 114*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 22*x^20 + 13*x^19 + 52*x^18 + 11*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 119*x^11 + 100*x^10 + 33*x^9 + 62*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 42*x^4 + 11*x^3 + 124*x^2 + 61*x + 94, x^95 + 15*x^93 + 14*x^92 + 37*x^91 + 108*x^90 + 67*x^89 + 106*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 14*x^84 + 89*x^83 + 52*x^82 + 95*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 67*x^75 + 4*x^74 + 53*x^73 + 22*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 98*x^68 + 103*x^67 + 28*x^66 + x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 25*x^27 + 92*x^26 + 111*x^25 + 18*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 6*x^20 + 125*x^19 + 68*x^18 + 27*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 103*x^11 + 116*x^10 + 49*x^9 + 94*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 122*x^4 + 91*x^3 + 44*x^2 + 109*x + 30, x^95 + 15*x^93 + 70*x^92 + 37*x^91 + 108*x^90 + 35*x^89 + 98*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 38*x^84 + 89*x^83 + 116*x^82 + 127*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 67*x^75 + 4*x^74 + 85*x^73 + 94*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 74*x^68 + 103*x^67 + 92*x^66 + 97*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 25*x^27 + 92*x^26 + 79*x^25 + 106*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 126*x^20 + 125*x^19 + 4*x^18 + 59*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 103*x^11 + 116*x^10 + 81*x^9 + 6*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 66*x^4 + 91*x^3 + 108*x^2 + 77*x + 38, x^95 + 15*x^93 + 114*x^92 + 101*x^91 + 84*x^90 + 3*x^89 + 86*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 114*x^84 + 25*x^83 + 12*x^82 + 31*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 3*x^75 + 60*x^74 + 117*x^73 + 42*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 30*x^68 + 39*x^67 + 36*x^66 + 65*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 89*x^27 + 100*x^26 + 47*x^25 + 46*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 122*x^20 + 61*x^19 + 124*x^18 + 91*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 39*x^11 + 76*x^10 + 113*x^9 + 98*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 6*x^4 + 27*x^3 + 20*x^2 + 45*x + 34, x^95 + 15*x^93 + 110*x^92 + 53*x^91 + 60*x^90 + 51*x^89 + 58*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 14*x^84 + 9*x^83 + 36*x^82 + 47*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 115*x^75 + 116*x^74 + 5*x^73 + 6*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 34*x^68 + 119*x^67 + 108*x^66 + 113*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 105*x^27 + 108*x^26 + 31*x^25 + 34*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 6*x^20 + 109*x^19 + 116*x^18 + 43*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 87*x^11 + 36*x^10 + 65*x^9 + 14*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 58*x^4 + 43*x^3 + 60*x^2 + 29*x + 110, x^95 + 15*x^93 + 34*x^92 + 85*x^91 + 68*x^90 + 83*x^89 + 86*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 66*x^84 + 105*x^83 + 92*x^82 + 15*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 83*x^75 + 12*x^74 + 101*x^73 + 106*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 14*x^68 + 23*x^67 + 20*x^66 + 17*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 9*x^27 + 20*x^26 + 63*x^25 + 46*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 10*x^20 + 77*x^19 + 12*x^18 + 11*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 55*x^11 + 92*x^10 + 33*x^9 + 34*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 54*x^4 + 75*x^3 + 68*x^2 + 61*x + 2, x^95 + 15*x^93 + 102*x^92 + 21*x^91 + 92*x^90 + 115*x^89 + 18*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 38*x^84 + 41*x^83 + 68*x^82 + 111*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 19*x^75 + 84*x^74 + 69*x^73 + 110*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 10*x^68 + 87*x^67 + 76*x^66 + 49*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 73*x^27 + 12*x^26 + 95*x^25 + 90*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 126*x^20 + 13*x^19 + 20*x^18 + 107*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 119*x^11 + 4*x^10 + x^9 + 86*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 2*x^4 + 11*x^3 + 28*x^2 + 93*x + 86, x^95 + 15*x^93 + 82*x^92 + 69*x^91 + 20*x^90 + 99*x^89 + 54*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 82*x^84 + 57*x^83 + 76*x^82 + 63*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 35*x^75 + 124*x^74 + 21*x^73 + 74*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 62*x^68 + 7*x^67 + 100*x^66 + 33*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 57*x^27 + 36*x^26 + 15*x^25 + 14*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 90*x^20 + 93*x^19 + 60*x^18 + 123*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 71*x^11 + 12*x^10 + 17*x^9 + 2*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 38*x^4 + 123*x^3 + 84*x^2 + 13*x + 66, x^95 + 15*x^93 + 30*x^92 + 101*x^91 + 12*x^90 + 67*x^89 + 90*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 30*x^84 + 25*x^83 + 20*x^82 + 95*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 3*x^75 + 100*x^74 + 53*x^73 + 38*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 82*x^68 + 39*x^67 + 60*x^66 + x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 89*x^27 + 124*x^26 + 111*x^25 + 66*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 86*x^20 + 61*x^19 + 36*x^18 + 27*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 39*x^11 + 84*x^10 + 49*x^9 + 46*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 42*x^4 + 27*x^3 + 76*x^2 + 109*x + 110, x^95 + 15*x^93 + 10*x^92 + 101*x^91 + 84*x^90 + 35*x^89 + 46*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 106*x^84 + 25*x^83 + 76*x^82 + 127*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 3*x^75 + 60*x^74 + 85*x^73 + 18*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 38*x^68 + 39*x^67 + 100*x^66 + 97*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 89*x^27 + 100*x^26 + 79*x^25 + 102*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 82*x^20 + 61*x^19 + 60*x^18 + 59*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 39*x^11 + 76*x^10 + 81*x^9 + 42*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 110*x^4 + 27*x^3 + 84*x^2 + 77*x + 74, x^95 + 15*x^93 + 66*x^92 + 101*x^91 + 52*x^90 + 67*x^89 + 70*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 66*x^84 + 25*x^83 + 44*x^82 + 95*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 3*x^75 + 92*x^74 + 53*x^73 + 58*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 78*x^68 + 39*x^67 + 4*x^66 + x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 89*x^27 + 68*x^26 + 111*x^25 + 94*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 10*x^20 + 61*x^19 + 28*x^18 + 27*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 39*x^11 + 108*x^10 + 49*x^9 + 50*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 118*x^4 + 27*x^3 + 116*x^2 + 109*x + 114, x^95 + 15*x^93 + 126*x^92 + 5*x^91 + 76*x^90 + 99*x^89 + 58*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 126*x^84 + 121*x^83 + 84*x^82 + 63*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 99*x^75 + 36*x^74 + 21*x^73 + 70*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 114*x^68 + 71*x^67 + 124*x^66 + 33*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 121*x^27 + 60*x^26 + 15*x^25 + 34*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 54*x^20 + 29*x^19 + 100*x^18 + 123*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 7*x^11 + 20*x^10 + 17*x^9 + 78*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 74*x^4 + 59*x^3 + 12*x^2 + 13*x + 14, x^95 + 15*x^93 + 6*x^92 + 117*x^91 + 92*x^90 + 19*x^89 + 50*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 70*x^84 + 73*x^83 + 68*x^82 + 79*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 51*x^75 + 84*x^74 + 37*x^73 + 78*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 106*x^68 + 55*x^67 + 76*x^66 + 81*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 41*x^27 + 12*x^26 + 127*x^25 + 122*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 30*x^20 + 45*x^19 + 20*x^18 + 75*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 23*x^11 + 4*x^10 + 97*x^9 + 54*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 98*x^4 + 107*x^3 + 28*x^2 + 125*x + 54, x^95 + 15*x^93 + 94*x^92 + 117*x^91 + 92*x^90 + 115*x^89 + 74*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 126*x^84 + 73*x^83 + 4*x^82 + 111*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 51*x^75 + 84*x^74 + 69*x^73 + 118*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 50*x^68 + 55*x^67 + 12*x^66 + 49*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 41*x^27 + 12*x^26 + 95*x^25 + 114*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 54*x^20 + 45*x^19 + 84*x^18 + 107*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 23*x^11 + 4*x^10 + x^9 + 62*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 10*x^4 + 107*x^3 + 92*x^2 + 93*x + 30, x^95 + 15*x^93 + 62*x^92 + 5*x^91 + 44*x^90 + 99*x^89 + 26*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 126*x^84 + 121*x^83 + 116*x^82 + 63*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 99*x^75 + 68*x^74 + 21*x^73 + 102*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 114*x^68 + 71*x^67 + 92*x^66 + 33*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 121*x^27 + 28*x^26 + 15*x^25 + 2*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 54*x^20 + 29*x^19 + 4*x^18 + 123*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 7*x^11 + 52*x^10 + 17*x^9 + 110*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 74*x^4 + 59*x^3 + 108*x^2 + 13*x + 110, x^95 + 15*x^93 + 82*x^92 + 37*x^91 + 84*x^90 + 67*x^89 + 54*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 82*x^84 + 89*x^83 + 12*x^82 + 95*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 67*x^75 + 60*x^74 + 53*x^73 + 74*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 62*x^68 + 103*x^67 + 36*x^66 + x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 25*x^27 + 100*x^26 + 111*x^25 + 14*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 90*x^20 + 125*x^19 + 124*x^18 + 27*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 103*x^11 + 76*x^10 + 49*x^9 + 2*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 38*x^4 + 91*x^3 + 20*x^2 + 109*x + 66, x^95 + 15*x^93 + 102*x^92 + 69*x^91 + 76*x^90 + 3*x^89 + 34*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 6*x^84 + 57*x^83 + 20*x^82 + 31*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 35*x^75 + 36*x^74 + 117*x^73 + 30*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 106*x^68 + 7*x^67 + 60*x^66 + 65*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 57*x^27 + 60*x^26 + 47*x^25 + 42*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 94*x^20 + 93*x^19 + 36*x^18 + 91*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 71*x^11 + 20*x^10 + 113*x^9 + 70*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 98*x^4 + 123*x^3 + 76*x^2 + 45*x + 38, x^95 + 15*x^93 + 6*x^92 + 117*x^91 + 28*x^90 + 83*x^89 + 50*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 70*x^84 + 73*x^83 + 4*x^82 + 15*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 51*x^75 + 20*x^74 + 101*x^73 + 78*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 106*x^68 + 55*x^67 + 12*x^66 + 17*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 41*x^27 + 76*x^26 + 63*x^25 + 122*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 30*x^20 + 45*x^19 + 84*x^18 + 11*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 23*x^11 + 68*x^10 + 33*x^9 + 54*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 98*x^4 + 107*x^3 + 92*x^2 + 61*x + 54, x^95 + 15*x^93 + 34*x^92 + 117*x^91 + 100*x^90 + 115*x^89 + 118*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 2*x^84 + 73*x^83 + 60*x^82 + 111*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 51*x^75 + 108*x^74 + 69*x^73 + 74*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 78*x^68 + 55*x^67 + 52*x^66 + 49*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 41*x^27 + 52*x^26 + 95*x^25 + 78*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 74*x^20 + 45*x^19 + 108*x^18 + 107*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 23*x^11 + 60*x^10 + x^9 + 2*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 118*x^4 + 107*x^3 + 100*x^2 + 93*x + 34, x^95 + 15*x^93 + 58*x^92 + 21*x^91 + 4*x^90 + 115*x^89 + 46*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 58*x^84 + 41*x^83 + 92*x^82 + 111*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 19*x^75 + 76*x^74 + 69*x^73 + 82*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 22*x^68 + 87*x^67 + 20*x^66 + 49*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 73*x^27 + 84*x^26 + 95*x^25 + 102*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 98*x^20 + 13*x^19 + 12*x^18 + 107*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 119*x^11 + 28*x^10 + x^9 + 106*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 30*x^4 + 11*x^3 + 68*x^2 + 93*x + 42, x^95 + 15*x^93 + 6*x^92 + 53*x^91 + 92*x^90 + 19*x^89 + 114*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 70*x^84 + 9*x^83 + 68*x^82 + 79*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 115*x^75 + 84*x^74 + 37*x^73 + 14*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 106*x^68 + 119*x^67 + 76*x^66 + 81*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 105*x^27 + 12*x^26 + 127*x^25 + 58*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 30*x^20 + 109*x^19 + 20*x^18 + 75*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 87*x^11 + 4*x^10 + 97*x^9 + 118*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 98*x^4 + 43*x^3 + 28*x^2 + 125*x + 118, x^95 + 15*x^93 + 26*x^92 + 5*x^91 + 84*x^90 + 67*x^89 + 62*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 58*x^84 + 121*x^83 + 76*x^82 + 95*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 99*x^75 + 60*x^74 + 53*x^73 + 2*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 86*x^68 + 71*x^67 + 100*x^66 + x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 121*x^27 + 100*x^26 + 111*x^25 + 54*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 98*x^20 + 29*x^19 + 60*x^18 + 27*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 7*x^11 + 76*x^10 + 49*x^9 + 90*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 94*x^4 + 59*x^3 + 84*x^2 + 109*x + 58, x^95 + 15*x^93 + 26*x^92 + 117*x^91 + 36*x^90 + 19*x^89 + 110*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 90*x^84 + 73*x^83 + 60*x^82 + 79*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 51*x^75 + 44*x^74 + 37*x^73 + 18*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 118*x^68 + 55*x^67 + 52*x^66 + 81*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 41*x^27 + 116*x^26 + 127*x^25 + 38*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 2*x^20 + 45*x^19 + 108*x^18 + 75*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 23*x^11 + 124*x^10 + 97*x^9 + 42*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 126*x^4 + 107*x^3 + 100*x^2 + 125*x + 42, x^95 + 15*x^93 + 58*x^92 + 85*x^91 + 36*x^90 + 115*x^89 + 78*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 122*x^84 + 105*x^83 + 60*x^82 + 111*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 83*x^75 + 44*x^74 + 69*x^73 + 50*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 86*x^68 + 23*x^67 + 52*x^66 + 49*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 9*x^27 + 116*x^26 + 95*x^25 + 6*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 34*x^20 + 77*x^19 + 108*x^18 + 107*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 55*x^11 + 124*x^10 + x^9 + 74*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 94*x^4 + 75*x^3 + 100*x^2 + 93*x + 74, x^95 + 15*x^93 + 74*x^92 + 53*x^91 + 36*x^90 + 83*x^89 + 94*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 74*x^84 + 9*x^83 + 60*x^82 + 15*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 115*x^75 + 44*x^74 + 101*x^73 + 34*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 6*x^68 + 119*x^67 + 52*x^66 + 17*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 105*x^27 + 116*x^26 + 63*x^25 + 86*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 50*x^20 + 109*x^19 + 108*x^18 + 11*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 87*x^11 + 124*x^10 + 33*x^9 + 122*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 78*x^4 + 43*x^3 + 100*x^2 + 61*x + 58, x^95 + 15*x^93 + 22*x^92 + 21*x^91 + 60*x^90 + 51*x^89 + 98*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 86*x^84 + 41*x^83 + 100*x^82 + 47*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 19*x^75 + 116*x^74 + 5*x^73 + 30*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 90*x^68 + 87*x^67 + 44*x^66 + 113*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 73*x^27 + 108*x^26 + 31*x^25 + 106*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 110*x^20 + 13*x^19 + 52*x^18 + 43*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 119*x^11 + 36*x^10 + 65*x^9 + 70*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 18*x^4 + 11*x^3 + 124*x^2 + 29*x + 70, x^95 + 15*x^93 + 70*x^92 + 21*x^91 + 28*x^90 + 51*x^89 + 114*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 6*x^84 + 41*x^83 + 4*x^82 + 47*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 19*x^75 + 20*x^74 + 5*x^73 + 14*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 42*x^68 + 87*x^67 + 12*x^66 + 113*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 73*x^27 + 76*x^26 + 31*x^25 + 58*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 94*x^20 + 13*x^19 + 84*x^18 + 43*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 119*x^11 + 68*x^10 + 65*x^9 + 118*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 34*x^4 + 11*x^3 + 92*x^2 + 29*x + 118, x^95 + 15*x^93 + 42*x^92 + 37*x^91 + 84*x^90 + 35*x^89 + 14*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 10*x^84 + 89*x^83 + 76*x^82 + 127*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 67*x^75 + 60*x^74 + 85*x^73 + 50*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 6*x^68 + 103*x^67 + 100*x^66 + 97*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 25*x^27 + 100*x^26 + 79*x^25 + 70*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 114*x^20 + 125*x^19 + 60*x^18 + 59*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 103*x^11 + 76*x^10 + 81*x^9 + 74*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 78*x^4 + 91*x^3 + 84*x^2 + 77*x + 106, x^95 + 15*x^93 + 42*x^92 + 101*x^91 + 84*x^90 + 35*x^89 + 78*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 10*x^84 + 25*x^83 + 76*x^82 + 127*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 3*x^75 + 60*x^74 + 85*x^73 + 114*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 6*x^68 + 39*x^67 + 100*x^66 + 97*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 89*x^27 + 100*x^26 + 79*x^25 + 6*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 114*x^20 + 61*x^19 + 60*x^18 + 59*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 39*x^11 + 76*x^10 + 81*x^9 + 10*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 78*x^4 + 27*x^3 + 84*x^2 + 77*x + 42, x^95 + 15*x^93 + 50*x^92 + 53*x^91 + 100*x^90 + 115*x^89 + 6*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 82*x^84 + 9*x^83 + 60*x^82 + 111*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 115*x^75 + 108*x^74 + 69*x^73 + 58*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 126*x^68 + 119*x^67 + 52*x^66 + 49*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 105*x^27 + 52*x^26 + 95*x^25 + 30*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 90*x^20 + 109*x^19 + 108*x^18 + 107*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 87*x^11 + 60*x^10 + x^9 + 50*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 102*x^4 + 43*x^3 + 100*x^2 + 93*x + 18, x^95 + 15*x^93 + 62*x^92 + 101*x^91 + 44*x^90 + 67*x^89 + 90*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 126*x^84 + 25*x^83 + 116*x^82 + 95*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 3*x^75 + 68*x^74 + 53*x^73 + 38*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 114*x^68 + 39*x^67 + 92*x^66 + x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 89*x^27 + 28*x^26 + 111*x^25 + 66*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 54*x^20 + 61*x^19 + 4*x^18 + 27*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 39*x^11 + 52*x^10 + 49*x^9 + 46*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 74*x^4 + 27*x^3 + 108*x^2 + 109*x + 46, x^95 + 15*x^93 + 118*x^92 + 117*x^91 + 28*x^90 + 19*x^89 + 34*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 118*x^84 + 73*x^83 + 4*x^82 + 79*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 51*x^75 + 20*x^74 + 37*x^73 + 94*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 58*x^68 + 55*x^67 + 12*x^66 + 81*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 41*x^27 + 76*x^26 + 127*x^25 + 42*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 14*x^20 + 45*x^19 + 84*x^18 + 75*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 23*x^11 + 68*x^10 + 97*x^9 + 6*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 114*x^4 + 107*x^3 + 92*x^2 + 125*x + 70, x^95 + 15*x^93 + 30*x^92 + 53*x^91 + 92*x^90 + 115*x^89 + 74*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 62*x^84 + 9*x^83 + 4*x^82 + 111*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 115*x^75 + 84*x^74 + 69*x^73 + 118*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 114*x^68 + 119*x^67 + 12*x^66 + 49*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 105*x^27 + 12*x^26 + 95*x^25 + 114*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 118*x^20 + 109*x^19 + 84*x^18 + 107*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 87*x^11 + 4*x^10 + x^9 + 62*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 74*x^4 + 43*x^3 + 92*x^2 + 93*x + 30, x^95 + 15*x^93 + 2*x^92 + 117*x^91 + 4*x^90 + 51*x^89 + 118*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 34*x^84 + 73*x^83 + 28*x^82 + 47*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 51*x^75 + 76*x^74 + 5*x^73 + 74*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 46*x^68 + 55*x^67 + 84*x^66 + 113*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 41*x^27 + 84*x^26 + 31*x^25 + 78*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 106*x^20 + 45*x^19 + 76*x^18 + 43*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 23*x^11 + 28*x^10 + 65*x^9 + 2*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 86*x^4 + 107*x^3 + 4*x^2 + 29*x + 98, x^95 + 15*x^93 + 22*x^92 + 85*x^91 + 92*x^90 + 115*x^89 + 66*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 22*x^84 + 105*x^83 + 68*x^82 + 111*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 83*x^75 + 84*x^74 + 69*x^73 + 62*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 26*x^68 + 23*x^67 + 76*x^66 + 49*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 9*x^27 + 12*x^26 + 95*x^25 + 74*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 46*x^20 + 77*x^19 + 20*x^18 + 107*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 55*x^11 + 4*x^10 + x^9 + 102*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 82*x^4 + 75*x^3 + 28*x^2 + 93*x + 38, x^95 + 15*x^93 + 90*x^92 + 85*x^91 + 100*x^90 + 115*x^89 + 46*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 26*x^84 + 105*x^83 + 124*x^82 + 111*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 83*x^75 + 108*x^74 + 69*x^73 + 82*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 54*x^68 + 23*x^67 + 116*x^66 + 49*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 9*x^27 + 52*x^26 + 95*x^25 + 102*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 66*x^20 + 77*x^19 + 44*x^18 + 107*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 55*x^11 + 60*x^10 + x^9 + 106*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 62*x^4 + 75*x^3 + 36*x^2 + 93*x + 106, x^95 + 15*x^93 + 86*x^92 + 37*x^91 + 108*x^90 + 99*x^89 + 114*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 118*x^84 + 89*x^83 + 116*x^82 + 63*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 67*x^75 + 4*x^74 + 21*x^73 + 78*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 122*x^68 + 103*x^67 + 92*x^66 + 33*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 25*x^27 + 92*x^26 + 15*x^25 + 58*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 14*x^20 + 125*x^19 + 4*x^18 + 123*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 103*x^11 + 116*x^10 + 17*x^9 + 54*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 50*x^4 + 91*x^3 + 108*x^2 + 13*x + 22, x^95 + 15*x^93 + 122*x^92 + 101*x^91 + 84*x^90 + 35*x^89 + 94*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 26*x^84 + 25*x^83 + 76*x^82 + 127*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 3*x^75 + 60*x^74 + 85*x^73 + 98*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 118*x^68 + 39*x^67 + 100*x^66 + 97*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 89*x^27 + 100*x^26 + 79*x^25 + 86*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 66*x^20 + 61*x^19 + 60*x^18 + 59*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 39*x^11 + 76*x^10 + 81*x^9 + 58*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 126*x^4 + 27*x^3 + 84*x^2 + 77*x + 26, x^95 + 15*x^93 + 90*x^92 + 37*x^91 + 84*x^90 + 99*x^89 + 62*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 122*x^84 + 89*x^83 + 76*x^82 + 63*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 67*x^75 + 60*x^74 + 21*x^73 + 2*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 22*x^68 + 103*x^67 + 100*x^66 + 33*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 25*x^27 + 100*x^26 + 15*x^25 + 54*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 34*x^20 + 125*x^19 + 60*x^18 + 123*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 103*x^11 + 76*x^10 + 17*x^9 + 90*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 30*x^4 + 91*x^3 + 84*x^2 + 13*x + 58, x^95 + 15*x^93 + 74*x^92 + 85*x^91 + 100*x^90 + 115*x^89 + 94*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 74*x^84 + 105*x^83 + 124*x^82 + 111*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 83*x^75 + 108*x^74 + 69*x^73 + 34*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 6*x^68 + 23*x^67 + 116*x^66 + 49*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 9*x^27 + 52*x^26 + 95*x^25 + 86*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 50*x^20 + 77*x^19 + 44*x^18 + 107*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 55*x^11 + 60*x^10 + x^9 + 122*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 78*x^4 + 75*x^3 + 36*x^2 + 93*x + 58, x^95 + 15*x^93 + 122*x^92 + 53*x^91 + 36*x^90 + 19*x^89 + 14*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 58*x^84 + 9*x^83 + 60*x^82 + 79*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 115*x^75 + 44*x^74 + 37*x^73 + 114*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 22*x^68 + 119*x^67 + 52*x^66 + 81*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 105*x^27 + 116*x^26 + 127*x^25 + 70*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 98*x^20 + 109*x^19 + 108*x^18 + 75*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 87*x^11 + 124*x^10 + 97*x^9 + 10*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 30*x^4 + 43*x^3 + 100*x^2 + 125*x + 10, x^95 + 15*x^93 + 22*x^92 + 85*x^91 + 124*x^90 + 51*x^89 + 98*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 86*x^84 + 105*x^83 + 36*x^82 + 47*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 83*x^75 + 52*x^74 + 5*x^73 + 30*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 90*x^68 + 23*x^67 + 108*x^66 + 113*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 9*x^27 + 44*x^26 + 31*x^25 + 106*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 110*x^20 + 77*x^19 + 116*x^18 + 43*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 55*x^11 + 100*x^10 + 65*x^9 + 70*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 18*x^4 + 75*x^3 + 60*x^2 + 29*x + 70, x^95 + 15*x^93 + 70*x^92 + 101*x^91 + 44*x^90 + 35*x^89 + 98*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 38*x^84 + 25*x^83 + 52*x^82 + 127*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 3*x^75 + 68*x^74 + 85*x^73 + 94*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 74*x^68 + 39*x^67 + 28*x^66 + 97*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 89*x^27 + 28*x^26 + 79*x^25 + 106*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 126*x^20 + 61*x^19 + 68*x^18 + 59*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 39*x^11 + 52*x^10 + 81*x^9 + 6*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 66*x^4 + 27*x^3 + 44*x^2 + 77*x + 38, x^95 + 15*x^93 + 18*x^92 + 53*x^91 + 68*x^90 + 115*x^89 + 6*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 114*x^84 + 9*x^83 + 92*x^82 + 111*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 115*x^75 + 12*x^74 + 69*x^73 + 58*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 94*x^68 + 119*x^67 + 20*x^66 + 49*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 105*x^27 + 20*x^26 + 95*x^25 + 30*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 122*x^20 + 109*x^19 + 12*x^18 + 107*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 87*x^11 + 92*x^10 + x^9 + 50*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 70*x^4 + 43*x^3 + 68*x^2 + 93*x + 82, x^95 + 15*x^93 + 118*x^92 + 37*x^91 + 76*x^90 + 99*x^89 + 50*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 86*x^84 + 89*x^83 + 20*x^82 + 63*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 67*x^75 + 36*x^74 + 21*x^73 + 14*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 26*x^68 + 103*x^67 + 60*x^66 + 33*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 25*x^27 + 60*x^26 + 15*x^25 + 122*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 110*x^20 + 125*x^19 + 36*x^18 + 123*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 103*x^11 + 20*x^10 + 17*x^9 + 118*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 82*x^4 + 91*x^3 + 76*x^2 + 13*x + 22, x^95 + 15*x^93 + 62*x^92 + 37*x^91 + 44*x^90 + 67*x^89 + 26*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 126*x^84 + 89*x^83 + 116*x^82 + 95*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 67*x^75 + 68*x^74 + 53*x^73 + 102*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 114*x^68 + 103*x^67 + 92*x^66 + x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 25*x^27 + 28*x^26 + 111*x^25 + 2*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 54*x^20 + 125*x^19 + 4*x^18 + 27*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 103*x^11 + 52*x^10 + 49*x^9 + 110*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 74*x^4 + 91*x^3 + 108*x^2 + 109*x + 110, x^95 + 15*x^93 + 78*x^92 + 53*x^91 + 60*x^90 + 115*x^89 + 90*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 110*x^84 + 9*x^83 + 36*x^82 + 111*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 115*x^75 + 116*x^74 + 69*x^73 + 102*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 66*x^68 + 119*x^67 + 108*x^66 + 49*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 105*x^27 + 108*x^26 + 95*x^25 + 66*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 102*x^20 + 109*x^19 + 116*x^18 + 107*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 87*x^11 + 36*x^10 + x^9 + 110*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 90*x^4 + 43*x^3 + 60*x^2 + 93*x + 78, x^95 + 15*x^93 + 2*x^92 + 85*x^91 + 36*x^90 + 19*x^89 + 22*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 98*x^84 + 105*x^83 + 124*x^82 + 79*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 83*x^75 + 44*x^74 + 37*x^73 + 42*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 110*x^68 + 23*x^67 + 116*x^66 + 81*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 9*x^27 + 116*x^26 + 127*x^25 + 110*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 42*x^20 + 77*x^19 + 44*x^18 + 75*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 55*x^11 + 124*x^10 + 97*x^9 + 98*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 22*x^4 + 75*x^3 + 36*x^2 + 125*x + 2, x^95 + 15*x^93 + 6*x^92 + 117*x^91 + 60*x^90 + 83*x^89 + 18*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 6*x^84 + 73*x^83 + 100*x^82 + 15*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 51*x^75 + 116*x^74 + 101*x^73 + 110*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 42*x^68 + 55*x^67 + 44*x^66 + 17*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 41*x^27 + 108*x^26 + 63*x^25 + 90*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 94*x^20 + 45*x^19 + 52*x^18 + 11*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 23*x^11 + 36*x^10 + 33*x^9 + 86*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 34*x^4 + 107*x^3 + 124*x^2 + 61*x + 22, x^95 + 15*x^93 + 30*x^92 + 69*x^91 + 108*x^90 + 99*x^89 + 122*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 94*x^84 + 57*x^83 + 52*x^82 + 63*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 35*x^75 + 4*x^74 + 21*x^73 + 6*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 18*x^68 + 7*x^67 + 28*x^66 + 33*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 57*x^27 + 92*x^26 + 15*x^25 + 98*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 22*x^20 + 93*x^19 + 68*x^18 + 123*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 71*x^11 + 116*x^10 + 17*x^9 + 14*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 106*x^4 + 123*x^3 + 44*x^2 + 13*x + 14, x^95 + 15*x^93 + 14*x^92 + 101*x^91 + 76*x^90 + 3*x^89 + 10*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 78*x^84 + 25*x^83 + 84*x^82 + 31*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 3*x^75 + 36*x^74 + 117*x^73 + 118*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 34*x^68 + 39*x^67 + 124*x^66 + 65*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 89*x^27 + 60*x^26 + 47*x^25 + 50*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 70*x^20 + 61*x^19 + 100*x^18 + 91*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 39*x^11 + 20*x^10 + 113*x^9 + 62*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 58*x^4 + 27*x^3 + 12*x^2 + 45*x + 62, x^95 + 15*x^93 + 46*x^92 + 21*x^91 + 124*x^90 + 83*x^89 + 58*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 78*x^84 + 41*x^83 + 100*x^82 + 15*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 19*x^75 + 52*x^74 + 101*x^73 + 6*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 98*x^68 + 87*x^67 + 44*x^66 + 17*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 73*x^27 + 44*x^26 + 63*x^25 + 34*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 70*x^20 + 13*x^19 + 52*x^18 + 11*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 119*x^11 + 100*x^10 + 33*x^9 + 14*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 122*x^4 + 11*x^3 + 124*x^2 + 61*x + 110, x^95 + 15*x^93 + 26*x^92 + 85*x^91 + 100*x^90 + 51*x^89 + 46*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 90*x^84 + 105*x^83 + 124*x^82 + 47*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 83*x^75 + 108*x^74 + 5*x^73 + 82*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 118*x^68 + 23*x^67 + 116*x^66 + 113*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 9*x^27 + 52*x^26 + 31*x^25 + 102*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 2*x^20 + 77*x^19 + 44*x^18 + 43*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 55*x^11 + 60*x^10 + 65*x^9 + 106*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 126*x^4 + 75*x^3 + 36*x^2 + 29*x + 106, x^95 + 15*x^93 + 46*x^92 + 69*x^91 + 12*x^90 + 99*x^89 + 42*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 110*x^84 + 57*x^83 + 20*x^82 + 63*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 35*x^75 + 100*x^74 + 21*x^73 + 86*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 2*x^68 + 7*x^67 + 60*x^66 + 33*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 57*x^27 + 124*x^26 + 15*x^25 + 82*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 102*x^20 + 93*x^19 + 36*x^18 + 123*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 71*x^11 + 84*x^10 + 17*x^9 + 30*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 26*x^4 + 123*x^3 + 76*x^2 + 13*x + 30, x^95 + 15*x^93 + 42*x^92 + 21*x^91 + 100*x^90 + 115*x^89 + 126*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 42*x^84 + 41*x^83 + 124*x^82 + 111*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 19*x^75 + 108*x^74 + 69*x^73 + 2*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 38*x^68 + 87*x^67 + 116*x^66 + 49*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 73*x^27 + 52*x^26 + 95*x^25 + 118*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 18*x^20 + 13*x^19 + 44*x^18 + 107*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 119*x^11 + 60*x^10 + x^9 + 90*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 110*x^4 + 11*x^3 + 36*x^2 + 93*x + 26, x^95 + 15*x^93 + 2*x^92 + 85*x^91 + 68*x^90 + 83*x^89 + 54*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 34*x^84 + 105*x^83 + 92*x^82 + 15*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 83*x^75 + 12*x^74 + 101*x^73 + 10*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 46*x^68 + 23*x^67 + 20*x^66 + 17*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 9*x^27 + 20*x^26 + 63*x^25 + 14*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 106*x^20 + 77*x^19 + 12*x^18 + 11*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 55*x^11 + 92*x^10 + 33*x^9 + 66*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 86*x^4 + 75*x^3 + 68*x^2 + 61*x + 34, x^95 + 15*x^93 + 70*x^92 + 37*x^91 + 108*x^90 + 99*x^89 + 34*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 38*x^84 + 89*x^83 + 116*x^82 + 63*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 67*x^75 + 4*x^74 + 21*x^73 + 30*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 74*x^68 + 103*x^67 + 92*x^66 + 33*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 25*x^27 + 92*x^26 + 15*x^25 + 42*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 126*x^20 + 125*x^19 + 4*x^18 + 123*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 103*x^11 + 116*x^10 + 17*x^9 + 70*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 66*x^4 + 91*x^3 + 108*x^2 + 13*x + 102, x^95 + 15*x^93 + 58*x^92 + 21*x^91 + 4*x^90 + 51*x^89 + 110*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 58*x^84 + 41*x^83 + 92*x^82 + 47*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 19*x^75 + 76*x^74 + 5*x^73 + 18*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 22*x^68 + 87*x^67 + 20*x^66 + 113*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 73*x^27 + 84*x^26 + 31*x^25 + 38*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 98*x^20 + 13*x^19 + 12*x^18 + 43*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 119*x^11 + 28*x^10 + 65*x^9 + 42*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 30*x^4 + 11*x^3 + 68*x^2 + 29*x + 106, x^95 + 15*x^93 + 118*x^92 + 21*x^91 + 124*x^90 + 51*x^89 + 2*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 54*x^84 + 41*x^83 + 36*x^82 + 47*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 19*x^75 + 52*x^74 + 5*x^73 + 126*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 122*x^68 + 87*x^67 + 108*x^66 + 113*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 73*x^27 + 44*x^26 + 31*x^25 + 10*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 78*x^20 + 13*x^19 + 116*x^18 + 43*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 119*x^11 + 100*x^10 + 65*x^9 + 38*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 50*x^4 + 11*x^3 + 60*x^2 + 29*x + 38, x^95 + 15*x^93 + 34*x^92 + 5*x^91 + 52*x^90 + 99*x^89 + 102*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 34*x^84 + 121*x^83 + 44*x^82 + 63*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 99*x^75 + 92*x^74 + 21*x^73 + 26*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 110*x^68 + 71*x^67 + 4*x^66 + 33*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 121*x^27 + 68*x^26 + 15*x^25 + 126*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 106*x^20 + 29*x^19 + 28*x^18 + 123*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 7*x^11 + 108*x^10 + 17*x^9 + 18*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 22*x^4 + 59*x^3 + 116*x^2 + 13*x + 82, x^95 + 15*x^93 + 14*x^92 + 101*x^91 + 12*x^90 + 3*x^89 + 74*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 78*x^84 + 25*x^83 + 20*x^82 + 31*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 3*x^75 + 100*x^74 + 117*x^73 + 54*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 34*x^68 + 39*x^67 + 60*x^66 + 65*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 89*x^27 + 124*x^26 + 47*x^25 + 114*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 70*x^20 + 61*x^19 + 36*x^18 + 91*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 39*x^11 + 84*x^10 + 113*x^9 + 126*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 58*x^4 + 27*x^3 + 76*x^2 + 45*x + 126, x^95 + 15*x^93 + 30*x^92 + 69*x^91 + 44*x^90 + 99*x^89 + 58*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 94*x^84 + 57*x^83 + 116*x^82 + 63*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 35*x^75 + 68*x^74 + 21*x^73 + 70*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 18*x^68 + 7*x^67 + 92*x^66 + 33*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 57*x^27 + 28*x^26 + 15*x^25 + 34*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 22*x^20 + 93*x^19 + 4*x^18 + 123*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 71*x^11 + 52*x^10 + 17*x^9 + 78*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 106*x^4 + 123*x^3 + 108*x^2 + 13*x + 78, x^95 + 15*x^93 + 94*x^92 + 101*x^91 + 44*x^90 + 3*x^89 + 58*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 30*x^84 + 25*x^83 + 116*x^82 + 31*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 3*x^75 + 68*x^74 + 117*x^73 + 70*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 82*x^68 + 39*x^67 + 92*x^66 + 65*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 89*x^27 + 28*x^26 + 47*x^25 + 34*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 86*x^20 + 61*x^19 + 4*x^18 + 91*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 39*x^11 + 52*x^10 + 113*x^9 + 78*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 42*x^4 + 27*x^3 + 108*x^2 + 45*x + 78, x^95 + 15*x^93 + 78*x^92 + 69*x^91 + 108*x^90 + 35*x^89 + 42*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 78*x^84 + 57*x^83 + 52*x^82 + 127*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 35*x^75 + 4*x^74 + 85*x^73 + 86*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 34*x^68 + 7*x^67 + 28*x^66 + 97*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 57*x^27 + 92*x^26 + 79*x^25 + 82*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 70*x^20 + 93*x^19 + 68*x^18 + 59*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 71*x^11 + 116*x^10 + 81*x^9 + 30*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 58*x^4 + 123*x^3 + 44*x^2 + 77*x + 94, x^95 + 15*x^93 + 18*x^92 + 69*x^91 + 52*x^90 + 99*x^89 + 86*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 82*x^84 + 57*x^83 + 44*x^82 + 63*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 35*x^75 + 92*x^74 + 21*x^73 + 42*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 62*x^68 + 7*x^67 + 4*x^66 + 33*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 57*x^27 + 68*x^26 + 15*x^25 + 46*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 90*x^20 + 93*x^19 + 28*x^18 + 123*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 71*x^11 + 108*x^10 + 17*x^9 + 98*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 38*x^4 + 123*x^3 + 116*x^2 + 13*x + 98, x^95 + 15*x^93 + 22*x^92 + 69*x^91 + 108*x^90 + 67*x^89 + 50*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 54*x^84 + 57*x^83 + 116*x^82 + 95*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 35*x^75 + 4*x^74 + 53*x^73 + 14*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 58*x^68 + 7*x^67 + 92*x^66 + x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 57*x^27 + 92*x^26 + 111*x^25 + 122*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 78*x^20 + 93*x^19 + 4*x^18 + 27*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 71*x^11 + 116*x^10 + 49*x^9 + 118*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 114*x^4 + 123*x^3 + 108*x^2 + 109*x + 86, x^95 + 15*x^93 + 122*x^92 + 85*x^91 + 36*x^90 + 51*x^89 + 78*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 58*x^84 + 105*x^83 + 60*x^82 + 47*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 83*x^75 + 44*x^74 + 5*x^73 + 50*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 22*x^68 + 23*x^67 + 52*x^66 + 113*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 9*x^27 + 116*x^26 + 31*x^25 + 6*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 98*x^20 + 77*x^19 + 108*x^18 + 43*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 55*x^11 + 124*x^10 + 65*x^9 + 74*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 30*x^4 + 75*x^3 + 100*x^2 + 29*x + 74, x^95 + 15*x^93 + 58*x^92 + 21*x^91 + 36*x^90 + 51*x^89 + 78*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 122*x^84 + 41*x^83 + 60*x^82 + 47*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 19*x^75 + 44*x^74 + 5*x^73 + 50*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 86*x^68 + 87*x^67 + 52*x^66 + 113*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 73*x^27 + 116*x^26 + 31*x^25 + 6*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 34*x^20 + 13*x^19 + 108*x^18 + 43*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 119*x^11 + 124*x^10 + 65*x^9 + 74*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 94*x^4 + 11*x^3 + 100*x^2 + 29*x + 74, x^95 + 15*x^93 + 118*x^92 + 5*x^91 + 76*x^90 + 3*x^89 + 50*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 86*x^84 + 121*x^83 + 20*x^82 + 31*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 99*x^75 + 36*x^74 + 117*x^73 + 14*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 26*x^68 + 71*x^67 + 60*x^66 + 65*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 121*x^27 + 60*x^26 + 47*x^25 + 122*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 110*x^20 + 29*x^19 + 36*x^18 + 91*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 7*x^11 + 20*x^10 + 113*x^9 + 118*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 82*x^4 + 59*x^3 + 76*x^2 + 45*x + 22, x^95 + 15*x^93 + 114*x^92 + 21*x^91 + 100*x^90 + 19*x^89 + 70*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 18*x^84 + 41*x^83 + 60*x^82 + 79*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 19*x^75 + 108*x^74 + 37*x^73 + 122*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 62*x^68 + 87*x^67 + 52*x^66 + 81*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 73*x^27 + 52*x^26 + 127*x^25 + 94*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 26*x^20 + 13*x^19 + 108*x^18 + 75*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 119*x^11 + 60*x^10 + 97*x^9 + 114*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 38*x^4 + 11*x^3 + 100*x^2 + 125*x + 82, x^95 + 15*x^93 + 30*x^92 + 21*x^91 + 60*x^90 + 83*x^89 + 42*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 126*x^84 + 41*x^83 + 36*x^82 + 15*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 19*x^75 + 116*x^74 + 101*x^73 + 22*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 50*x^68 + 87*x^67 + 108*x^66 + 17*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 73*x^27 + 108*x^26 + 63*x^25 + 82*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 54*x^20 + 13*x^19 + 116*x^18 + 11*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 119*x^11 + 36*x^10 + 33*x^9 + 94*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 10*x^4 + 11*x^3 + 60*x^2 + 61*x + 126, x^95 + 15*x^93 + 22*x^92 + 101*x^91 + 76*x^90 + 99*x^89 + 18*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 118*x^84 + 25*x^83 + 20*x^82 + 63*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 3*x^75 + 36*x^74 + 21*x^73 + 46*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 122*x^68 + 39*x^67 + 60*x^66 + 33*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 89*x^27 + 60*x^26 + 15*x^25 + 90*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 14*x^20 + 61*x^19 + 36*x^18 + 123*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 39*x^11 + 20*x^10 + 17*x^9 + 22*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 50*x^4 + 27*x^3 + 76*x^2 + 13*x + 54, x^95 + 15*x^93 + 14*x^92 + 53*x^91 + 124*x^90 + 115*x^89 + 90*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 46*x^84 + 9*x^83 + 100*x^82 + 111*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 115*x^75 + 52*x^74 + 69*x^73 + 102*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 2*x^68 + 119*x^67 + 44*x^66 + 49*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 105*x^27 + 44*x^26 + 95*x^25 + 66*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 38*x^20 + 109*x^19 + 52*x^18 + 107*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 87*x^11 + 100*x^10 + x^9 + 110*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 26*x^4 + 43*x^3 + 124*x^2 + 93*x + 78, x^95 + 15*x^93 + 90*x^92 + 5*x^91 + 84*x^90 + 3*x^89 + 62*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 122*x^84 + 121*x^83 + 76*x^82 + 31*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 99*x^75 + 60*x^74 + 117*x^73 + 2*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 22*x^68 + 71*x^67 + 100*x^66 + 65*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 121*x^27 + 100*x^26 + 47*x^25 + 54*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 34*x^20 + 29*x^19 + 60*x^18 + 91*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 7*x^11 + 76*x^10 + 113*x^9 + 90*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 30*x^4 + 59*x^3 + 84*x^2 + 45*x + 58, x^95 + 15*x^93 + 118*x^92 + 85*x^91 + 60*x^90 + 51*x^89 + 2*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 54*x^84 + 105*x^83 + 100*x^82 + 47*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 83*x^75 + 116*x^74 + 5*x^73 + 126*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 122*x^68 + 23*x^67 + 44*x^66 + 113*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 9*x^27 + 108*x^26 + 31*x^25 + 10*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 78*x^20 + 77*x^19 + 52*x^18 + 43*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 55*x^11 + 36*x^10 + 65*x^9 + 38*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 50*x^4 + 75*x^3 + 124*x^2 + 29*x + 38, x^95 + 15*x^93 + 114*x^92 + 101*x^91 + 116*x^90 + 3*x^89 + 54*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 50*x^84 + 25*x^83 + 108*x^82 + 31*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 3*x^75 + 28*x^74 + 117*x^73 + 74*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 94*x^68 + 39*x^67 + 68*x^66 + 65*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 89*x^27 + 4*x^26 + 47*x^25 + 14*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 58*x^20 + 61*x^19 + 92*x^18 + 91*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 39*x^11 + 44*x^10 + 113*x^9 + 2*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 70*x^4 + 27*x^3 + 52*x^2 + 45*x + 2, x^95 + 15*x^93 + 42*x^92 + 101*x^91 + 52*x^90 + 99*x^89 + 46*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 74*x^84 + 25*x^83 + 108*x^82 + 63*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 3*x^75 + 92*x^74 + 21*x^73 + 18*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 70*x^68 + 39*x^67 + 68*x^66 + 33*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 89*x^27 + 68*x^26 + 15*x^25 + 102*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 50*x^20 + 61*x^19 + 92*x^18 + 123*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 39*x^11 + 108*x^10 + 17*x^9 + 42*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 14*x^4 + 27*x^3 + 52*x^2 + 13*x + 10, x^95 + 15*x^93 + 46*x^92 + 117*x^91 + 92*x^90 + 51*x^89 + 26*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 14*x^84 + 73*x^83 + 4*x^82 + 47*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 51*x^75 + 84*x^74 + 5*x^73 + 38*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 34*x^68 + 55*x^67 + 12*x^66 + 113*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 41*x^27 + 12*x^26 + 31*x^25 + 2*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 6*x^20 + 45*x^19 + 84*x^18 + 43*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 23*x^11 + 4*x^10 + 65*x^9 + 46*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 58*x^4 + 107*x^3 + 92*x^2 + 29*x + 78, x^95 + 15*x^93 + 34*x^92 + 5*x^91 + 52*x^90 + 35*x^89 + 38*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 34*x^84 + 121*x^83 + 44*x^82 + 127*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 99*x^75 + 92*x^74 + 85*x^73 + 90*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 110*x^68 + 71*x^67 + 4*x^66 + 97*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 121*x^27 + 68*x^26 + 79*x^25 + 62*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 106*x^20 + 29*x^19 + 28*x^18 + 59*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 7*x^11 + 108*x^10 + 81*x^9 + 82*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 22*x^4 + 59*x^3 + 116*x^2 + 77*x + 18, x^95 + 15*x^93 + 26*x^92 + 37*x^91 + 116*x^90 + 35*x^89 + 30*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 122*x^84 + 89*x^83 + 44*x^82 + 127*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 67*x^75 + 28*x^74 + 85*x^73 + 34*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 22*x^68 + 103*x^67 + 4*x^66 + 97*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 25*x^27 + 4*x^26 + 79*x^25 + 22*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 34*x^20 + 125*x^19 + 28*x^18 + 59*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 103*x^11 + 44*x^10 + 81*x^9 + 122*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 30*x^4 + 91*x^3 + 116*x^2 + 77*x + 26, x^95 + 15*x^93 + 66*x^92 + 117*x^91 + 68*x^90 + 115*x^89 + 54*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 98*x^84 + 73*x^83 + 92*x^82 + 111*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 51*x^75 + 12*x^74 + 69*x^73 + 10*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 110*x^68 + 55*x^67 + 20*x^66 + 49*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 41*x^27 + 20*x^26 + 95*x^25 + 14*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 42*x^20 + 45*x^19 + 12*x^18 + 107*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 23*x^11 + 92*x^10 + x^9 + 66*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 22*x^4 + 107*x^3 + 68*x^2 + 93*x + 34, x^95 + 15*x^93 + 26*x^92 + 37*x^91 + 52*x^90 + 99*x^89 + 30*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 122*x^84 + 89*x^83 + 108*x^82 + 63*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 67*x^75 + 92*x^74 + 21*x^73 + 34*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 22*x^68 + 103*x^67 + 68*x^66 + 33*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 25*x^27 + 68*x^26 + 15*x^25 + 22*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 34*x^20 + 125*x^19 + 92*x^18 + 123*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 103*x^11 + 108*x^10 + 17*x^9 + 122*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 30*x^4 + 91*x^3 + 52*x^2 + 13*x + 26, x^95 + 15*x^93 + 70*x^92 + 117*x^91 + 124*x^90 + 19*x^89 + 82*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 70*x^84 + 73*x^83 + 36*x^82 + 79*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 51*x^75 + 52*x^74 + 37*x^73 + 46*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 106*x^68 + 55*x^67 + 108*x^66 + 81*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 41*x^27 + 44*x^26 + 127*x^25 + 26*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 30*x^20 + 45*x^19 + 116*x^18 + 75*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 23*x^11 + 100*x^10 + 97*x^9 + 22*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 98*x^4 + 107*x^3 + 60*x^2 + 125*x + 86, x^95 + 15*x^93 + 42*x^92 + 21*x^91 + 68*x^90 + 51*x^89 + 94*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 106*x^84 + 41*x^83 + 28*x^82 + 47*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 19*x^75 + 12*x^74 + 5*x^73 + 34*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 102*x^68 + 87*x^67 + 84*x^66 + 113*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 73*x^27 + 20*x^26 + 31*x^25 + 86*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 82*x^20 + 13*x^19 + 76*x^18 + 43*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 119*x^11 + 92*x^10 + 65*x^9 + 122*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 46*x^4 + 11*x^3 + 4*x^2 + 29*x + 122, x^95 + 15*x^93 + 26*x^92 + 85*x^91 + 36*x^90 + 51*x^89 + 110*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 90*x^84 + 105*x^83 + 60*x^82 + 47*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 83*x^75 + 44*x^74 + 5*x^73 + 18*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 118*x^68 + 23*x^67 + 52*x^66 + 113*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 9*x^27 + 116*x^26 + 31*x^25 + 38*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 2*x^20 + 77*x^19 + 108*x^18 + 43*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 55*x^11 + 124*x^10 + 65*x^9 + 42*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 126*x^4 + 75*x^3 + 100*x^2 + 29*x + 42, x^95 + 15*x^93 + 98*x^92 + 117*x^91 + 4*x^90 + 115*x^89 + 22*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 2*x^84 + 73*x^83 + 28*x^82 + 111*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 51*x^75 + 76*x^74 + 69*x^73 + 42*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 78*x^68 + 55*x^67 + 84*x^66 + 49*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 41*x^27 + 84*x^26 + 95*x^25 + 110*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 74*x^20 + 45*x^19 + 76*x^18 + 107*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 23*x^11 + 28*x^10 + x^9 + 98*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 118*x^4 + 107*x^3 + 4*x^2 + 93*x + 66, x^95 + 15*x^93 + 50*x^92 + 21*x^91 + 36*x^90 + 19*x^89 + 70*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 82*x^84 + 41*x^83 + 124*x^82 + 79*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 19*x^75 + 44*x^74 + 37*x^73 + 122*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 126*x^68 + 87*x^67 + 116*x^66 + 81*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 73*x^27 + 116*x^26 + 127*x^25 + 94*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 90*x^20 + 13*x^19 + 44*x^18 + 75*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 119*x^11 + 124*x^10 + 97*x^9 + 114*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 102*x^4 + 11*x^3 + 36*x^2 + 125*x + 82, x^95 + 15*x^93 + 18*x^92 + 37*x^91 + 52*x^90 + 67*x^89 + 22*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 82*x^84 + 89*x^83 + 44*x^82 + 95*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 67*x^75 + 92*x^74 + 53*x^73 + 106*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 62*x^68 + 103*x^67 + 4*x^66 + x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 25*x^27 + 68*x^26 + 111*x^25 + 110*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 90*x^20 + 125*x^19 + 28*x^18 + 27*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 103*x^11 + 108*x^10 + 49*x^9 + 34*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 38*x^4 + 91*x^3 + 116*x^2 + 109*x + 34, x^95 + 15*x^93 + 38*x^92 + 21*x^91 + 28*x^90 + 51*x^89 + 82*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 102*x^84 + 41*x^83 + 4*x^82 + 47*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 19*x^75 + 20*x^74 + 5*x^73 + 46*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 74*x^68 + 87*x^67 + 12*x^66 + 113*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 73*x^27 + 76*x^26 + 31*x^25 + 26*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 62*x^20 + 13*x^19 + 84*x^18 + 43*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 119*x^11 + 68*x^10 + 65*x^9 + 22*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 66*x^4 + 11*x^3 + 92*x^2 + 29*x + 22, x^95 + 15*x^93 + 118*x^92 + 69*x^91 + 76*x^90 + 67*x^89 + 50*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 86*x^84 + 57*x^83 + 20*x^82 + 95*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 35*x^75 + 36*x^74 + 53*x^73 + 14*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 26*x^68 + 7*x^67 + 60*x^66 + x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 57*x^27 + 60*x^26 + 111*x^25 + 122*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 110*x^20 + 93*x^19 + 36*x^18 + 27*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 71*x^11 + 20*x^10 + 49*x^9 + 118*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 82*x^4 + 123*x^3 + 76*x^2 + 109*x + 22, x^95 + 15*x^93 + 82*x^92 + 37*x^91 + 116*x^90 + 3*x^89 + 86*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 18*x^84 + 89*x^83 + 108*x^82 + 31*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 67*x^75 + 28*x^74 + 117*x^73 + 42*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 126*x^68 + 103*x^67 + 68*x^66 + 65*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 25*x^27 + 4*x^26 + 47*x^25 + 46*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 26*x^20 + 125*x^19 + 92*x^18 + 91*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 103*x^11 + 44*x^10 + 113*x^9 + 98*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 102*x^4 + 91*x^3 + 52*x^2 + 45*x + 98, x^95 + 15*x^93 + 94*x^92 + 53*x^91 + 60*x^90 + 51*x^89 + 106*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 62*x^84 + 9*x^83 + 36*x^82 + 47*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 115*x^75 + 116*x^74 + 5*x^73 + 86*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 114*x^68 + 119*x^67 + 108*x^66 + 113*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 105*x^27 + 108*x^26 + 31*x^25 + 18*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 118*x^20 + 109*x^19 + 116*x^18 + 43*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 87*x^11 + 36*x^10 + 65*x^9 + 30*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 74*x^4 + 43*x^3 + 60*x^2 + 29*x + 62, x^95 + 15*x^93 + 26*x^92 + 85*x^91 + 4*x^90 + 51*x^89 + 14*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 26*x^84 + 105*x^83 + 92*x^82 + 47*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 83*x^75 + 76*x^74 + 5*x^73 + 114*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 54*x^68 + 23*x^67 + 20*x^66 + 113*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 9*x^27 + 84*x^26 + 31*x^25 + 70*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 66*x^20 + 77*x^19 + 12*x^18 + 43*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 55*x^11 + 28*x^10 + 65*x^9 + 10*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 62*x^4 + 75*x^3 + 68*x^2 + 29*x + 74, x^95 + 15*x^93 + 70*x^92 + 21*x^91 + 60*x^90 + 115*x^89 + 18*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 70*x^84 + 41*x^83 + 100*x^82 + 111*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 19*x^75 + 116*x^74 + 69*x^73 + 110*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 106*x^68 + 87*x^67 + 44*x^66 + 49*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 73*x^27 + 108*x^26 + 95*x^25 + 90*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 30*x^20 + 13*x^19 + 52*x^18 + 107*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 119*x^11 + 36*x^10 + x^9 + 86*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 98*x^4 + 11*x^3 + 124*x^2 + 93*x + 22, x^95 + 15*x^93 + 78*x^92 + 85*x^91 + 92*x^90 + 83*x^89 + 58*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 46*x^84 + 105*x^83 + 4*x^82 + 15*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 83*x^75 + 84*x^74 + 101*x^73 + 6*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 2*x^68 + 23*x^67 + 12*x^66 + 17*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 9*x^27 + 12*x^26 + 63*x^25 + 34*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 38*x^20 + 77*x^19 + 84*x^18 + 11*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 55*x^11 + 4*x^10 + 33*x^9 + 14*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 26*x^4 + 75*x^3 + 92*x^2 + 61*x + 46, x^95 + 15*x^93 + 94*x^92 + 85*x^91 + 60*x^90 + 83*x^89 + 42*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 62*x^84 + 105*x^83 + 36*x^82 + 15*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 83*x^75 + 116*x^74 + 101*x^73 + 22*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 114*x^68 + 23*x^67 + 108*x^66 + 17*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 9*x^27 + 108*x^26 + 63*x^25 + 82*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 118*x^20 + 77*x^19 + 116*x^18 + 11*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 55*x^11 + 36*x^10 + 33*x^9 + 94*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 74*x^4 + 75*x^3 + 60*x^2 + 61*x + 126, x^95 + 15*x^93 + 26*x^92 + 69*x^91 + 84*x^90 + 67*x^89 + 126*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 58*x^84 + 57*x^83 + 76*x^82 + 95*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 35*x^75 + 60*x^74 + 53*x^73 + 66*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 86*x^68 + 7*x^67 + 100*x^66 + x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 57*x^27 + 100*x^26 + 111*x^25 + 118*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 98*x^20 + 93*x^19 + 60*x^18 + 27*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 71*x^11 + 76*x^10 + 49*x^9 + 26*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 94*x^4 + 123*x^3 + 84*x^2 + 109*x + 122, x^95 + 15*x^93 + 82*x^92 + 101*x^91 + 116*x^90 + 67*x^89 + 86*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 18*x^84 + 25*x^83 + 108*x^82 + 95*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 3*x^75 + 28*x^74 + 53*x^73 + 42*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 126*x^68 + 39*x^67 + 68*x^66 + x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 89*x^27 + 4*x^26 + 111*x^25 + 46*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 26*x^20 + 61*x^19 + 92*x^18 + 27*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 39*x^11 + 44*x^10 + 49*x^9 + 98*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 102*x^4 + 27*x^3 + 52*x^2 + 109*x + 98, x^95 + 15*x^93 + 2*x^92 + 101*x^91 + 116*x^90 + 3*x^89 + 6*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 2*x^84 + 25*x^83 + 108*x^82 + 31*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 3*x^75 + 28*x^74 + 117*x^73 + 122*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 14*x^68 + 39*x^67 + 68*x^66 + 65*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 89*x^27 + 4*x^26 + 47*x^25 + 30*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 74*x^20 + 61*x^19 + 92*x^18 + 91*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 39*x^11 + 44*x^10 + 113*x^9 + 114*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 54*x^4 + 27*x^3 + 52*x^2 + 45*x + 50, x^95 + 15*x^93 + 126*x^92 + 5*x^91 + 12*x^90 + 99*x^89 + 122*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 126*x^84 + 121*x^83 + 20*x^82 + 63*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 99*x^75 + 100*x^74 + 21*x^73 + 6*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 114*x^68 + 71*x^67 + 60*x^66 + 33*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 121*x^27 + 124*x^26 + 15*x^25 + 98*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 54*x^20 + 29*x^19 + 36*x^18 + 123*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 7*x^11 + 84*x^10 + 17*x^9 + 14*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 74*x^4 + 59*x^3 + 76*x^2 + 13*x + 78, x^95 + 15*x^93 + 34*x^92 + 117*x^91 + 36*x^90 + 51*x^89 + 118*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 2*x^84 + 73*x^83 + 124*x^82 + 47*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 51*x^75 + 44*x^74 + 5*x^73 + 74*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 78*x^68 + 55*x^67 + 116*x^66 + 113*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 41*x^27 + 116*x^26 + 31*x^25 + 78*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 74*x^20 + 45*x^19 + 44*x^18 + 43*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 23*x^11 + 124*x^10 + 65*x^9 + 2*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 118*x^4 + 107*x^3 + 36*x^2 + 29*x + 34, x^95 + 15*x^93 + 102*x^92 + 5*x^91 + 76*x^90 + 3*x^89 + 98*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 6*x^84 + 121*x^83 + 20*x^82 + 31*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 99*x^75 + 36*x^74 + 117*x^73 + 94*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 106*x^68 + 71*x^67 + 60*x^66 + 65*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 121*x^27 + 60*x^26 + 47*x^25 + 106*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 94*x^20 + 29*x^19 + 36*x^18 + 91*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 7*x^11 + 20*x^10 + 113*x^9 + 6*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 98*x^4 + 59*x^3 + 76*x^2 + 45*x + 102, x^95 + 15*x^93 + 86*x^92 + 101*x^91 + 108*x^90 + 99*x^89 + 50*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 118*x^84 + 25*x^83 + 116*x^82 + 63*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 3*x^75 + 4*x^74 + 21*x^73 + 14*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 122*x^68 + 39*x^67 + 92*x^66 + 33*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 89*x^27 + 92*x^26 + 15*x^25 + 122*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 14*x^20 + 61*x^19 + 4*x^18 + 123*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 39*x^11 + 116*x^10 + 17*x^9 + 118*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 50*x^4 + 27*x^3 + 108*x^2 + 13*x + 86, x^95 + 15*x^93 + 82*x^92 + 117*x^91 + 100*x^90 + 51*x^89 + 38*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 114*x^84 + 73*x^83 + 60*x^82 + 47*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 51*x^75 + 108*x^74 + 5*x^73 + 26*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 94*x^68 + 55*x^67 + 52*x^66 + 113*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 41*x^27 + 52*x^26 + 31*x^25 + 62*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 122*x^20 + 45*x^19 + 108*x^18 + 43*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 23*x^11 + 60*x^10 + 65*x^9 + 18*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 70*x^4 + 107*x^3 + 100*x^2 + 29*x + 114, x^95 + 15*x^93 + 46*x^92 + 85*x^91 + 124*x^90 + 83*x^89 + 122*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 78*x^84 + 105*x^83 + 100*x^82 + 15*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 83*x^75 + 52*x^74 + 101*x^73 + 70*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 98*x^68 + 23*x^67 + 44*x^66 + 17*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 9*x^27 + 44*x^26 + 63*x^25 + 98*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 70*x^20 + 77*x^19 + 52*x^18 + 11*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 55*x^11 + 100*x^10 + 33*x^9 + 78*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 122*x^4 + 75*x^3 + 124*x^2 + 61*x + 46, x^95 + 15*x^93 + 14*x^92 + 101*x^91 + 44*x^90 + 3*x^89 + 42*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 14*x^84 + 25*x^83 + 116*x^82 + 31*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 3*x^75 + 68*x^74 + 117*x^73 + 86*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 98*x^68 + 39*x^67 + 92*x^66 + 65*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 89*x^27 + 28*x^26 + 47*x^25 + 82*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 6*x^20 + 61*x^19 + 4*x^18 + 91*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 39*x^11 + 52*x^10 + 113*x^9 + 30*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 122*x^4 + 27*x^3 + 108*x^2 + 45*x + 94, x^95 + 15*x^93 + 86*x^92 + 69*x^91 + 108*x^90 + 3*x^89 + 50*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 118*x^84 + 57*x^83 + 116*x^82 + 31*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 35*x^75 + 4*x^74 + 117*x^73 + 14*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 122*x^68 + 7*x^67 + 92*x^66 + 65*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 57*x^27 + 92*x^26 + 47*x^25 + 122*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 14*x^20 + 93*x^19 + 4*x^18 + 91*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 71*x^11 + 116*x^10 + 113*x^9 + 118*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 50*x^4 + 123*x^3 + 108*x^2 + 45*x + 86, x^95 + 15*x^93 + 78*x^92 + 69*x^91 + 12*x^90 + 99*x^89 + 74*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 14*x^84 + 57*x^83 + 20*x^82 + 63*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 35*x^75 + 100*x^74 + 21*x^73 + 54*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 98*x^68 + 7*x^67 + 60*x^66 + 33*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 57*x^27 + 124*x^26 + 15*x^25 + 114*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 6*x^20 + 93*x^19 + 36*x^18 + 123*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 71*x^11 + 84*x^10 + 17*x^9 + 126*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 122*x^4 + 123*x^3 + 76*x^2 + 13*x + 126, x^95 + 15*x^93 + 122*x^92 + 37*x^91 + 84*x^90 + 99*x^89 + 94*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 26*x^84 + 89*x^83 + 76*x^82 + 63*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 67*x^75 + 60*x^74 + 21*x^73 + 98*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 118*x^68 + 103*x^67 + 100*x^66 + 33*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 25*x^27 + 100*x^26 + 15*x^25 + 86*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 66*x^20 + 125*x^19 + 60*x^18 + 123*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 103*x^11 + 76*x^10 + 17*x^9 + 58*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 126*x^4 + 91*x^3 + 84*x^2 + 13*x + 26, x^95 + 15*x^93 + 22*x^92 + 69*x^91 + 76*x^90 + 3*x^89 + 18*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 118*x^84 + 57*x^83 + 20*x^82 + 31*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 35*x^75 + 36*x^74 + 117*x^73 + 46*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 122*x^68 + 7*x^67 + 60*x^66 + 65*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 57*x^27 + 60*x^26 + 47*x^25 + 90*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 14*x^20 + 93*x^19 + 36*x^18 + 91*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 71*x^11 + 20*x^10 + 113*x^9 + 22*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 50*x^4 + 123*x^3 + 76*x^2 + 45*x + 54, x^95 + 15*x^93 + 18*x^92 + 21*x^91 + 100*x^90 + 19*x^89 + 102*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 50*x^84 + 41*x^83 + 60*x^82 + 79*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 19*x^75 + 108*x^74 + 37*x^73 + 90*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 30*x^68 + 87*x^67 + 52*x^66 + 81*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 73*x^27 + 52*x^26 + 127*x^25 + 126*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 58*x^20 + 13*x^19 + 108*x^18 + 75*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 119*x^11 + 60*x^10 + 97*x^9 + 82*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 6*x^4 + 11*x^3 + 100*x^2 + 125*x + 50, x^95 + 15*x^93 + 74*x^92 + 53*x^91 + 36*x^90 + 19*x^89 + 30*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 74*x^84 + 9*x^83 + 60*x^82 + 79*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 115*x^75 + 44*x^74 + 37*x^73 + 98*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 6*x^68 + 119*x^67 + 52*x^66 + 81*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 105*x^27 + 116*x^26 + 127*x^25 + 22*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 50*x^20 + 109*x^19 + 108*x^18 + 75*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 87*x^11 + 124*x^10 + 97*x^9 + 58*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 78*x^4 + 43*x^3 + 100*x^2 + 125*x + 122, x^95 + 15*x^93 + 26*x^92 + 5*x^91 + 52*x^90 + 3*x^89 + 30*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 122*x^84 + 121*x^83 + 108*x^82 + 31*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 99*x^75 + 92*x^74 + 117*x^73 + 34*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 22*x^68 + 71*x^67 + 68*x^66 + 65*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 121*x^27 + 68*x^26 + 47*x^25 + 22*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 34*x^20 + 29*x^19 + 92*x^18 + 91*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 7*x^11 + 108*x^10 + 113*x^9 + 122*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 30*x^4 + 59*x^3 + 52*x^2 + 45*x + 26, x^95 + 15*x^93 + 22*x^92 + 21*x^91 + 124*x^90 + 115*x^89 + 98*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 86*x^84 + 41*x^83 + 36*x^82 + 111*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 19*x^75 + 52*x^74 + 69*x^73 + 30*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 90*x^68 + 87*x^67 + 108*x^66 + 49*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 73*x^27 + 44*x^26 + 95*x^25 + 106*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 110*x^20 + 13*x^19 + 116*x^18 + 107*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 119*x^11 + 100*x^10 + x^9 + 70*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 18*x^4 + 11*x^3 + 60*x^2 + 93*x + 70, x^95 + 15*x^93 + 82*x^92 + 101*x^91 + 116*x^90 + 3*x^89 + 22*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 18*x^84 + 25*x^83 + 108*x^82 + 31*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 3*x^75 + 28*x^74 + 117*x^73 + 106*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 126*x^68 + 39*x^67 + 68*x^66 + 65*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 89*x^27 + 4*x^26 + 47*x^25 + 110*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 26*x^20 + 61*x^19 + 92*x^18 + 91*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 39*x^11 + 44*x^10 + 113*x^9 + 34*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 102*x^4 + 27*x^3 + 52*x^2 + 45*x + 34, x^95 + 15*x^93 + 38*x^92 + 53*x^91 + 124*x^90 + 19*x^89 + 114*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 38*x^84 + 9*x^83 + 36*x^82 + 79*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 115*x^75 + 52*x^74 + 37*x^73 + 14*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 10*x^68 + 119*x^67 + 108*x^66 + 81*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 105*x^27 + 44*x^26 + 127*x^25 + 58*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 126*x^20 + 109*x^19 + 116*x^18 + 75*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 87*x^11 + 100*x^10 + 97*x^9 + 118*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 2*x^4 + 43*x^3 + 60*x^2 + 125*x + 54, x^95 + 15*x^93 + 42*x^92 + 85*x^91 + 36*x^90 + 51*x^89 + 62*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 42*x^84 + 105*x^83 + 60*x^82 + 47*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 83*x^75 + 44*x^74 + 5*x^73 + 66*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 38*x^68 + 23*x^67 + 52*x^66 + 113*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 9*x^27 + 116*x^26 + 31*x^25 + 54*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 18*x^20 + 77*x^19 + 108*x^18 + 43*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 55*x^11 + 124*x^10 + 65*x^9 + 26*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 110*x^4 + 75*x^3 + 100*x^2 + 29*x + 90, x^95 + 15*x^93 + 122*x^92 + 117*x^91 + 36*x^90 + 83*x^89 + 14*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 58*x^84 + 73*x^83 + 60*x^82 + 15*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 51*x^75 + 44*x^74 + 101*x^73 + 114*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 22*x^68 + 55*x^67 + 52*x^66 + 17*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 41*x^27 + 116*x^26 + 63*x^25 + 70*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 98*x^20 + 45*x^19 + 108*x^18 + 11*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 23*x^11 + 124*x^10 + 33*x^9 + 10*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 30*x^4 + 107*x^3 + 100*x^2 + 61*x + 10, x^95 + 15*x^93 + 42*x^92 + 5*x^91 + 116*x^90 + 67*x^89 + 110*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 74*x^84 + 121*x^83 + 44*x^82 + 95*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 99*x^75 + 28*x^74 + 53*x^73 + 82*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 70*x^68 + 71*x^67 + 4*x^66 + x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 121*x^27 + 4*x^26 + 111*x^25 + 38*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 50*x^20 + 29*x^19 + 28*x^18 + 27*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 7*x^11 + 44*x^10 + 49*x^9 + 106*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 14*x^4 + 59*x^3 + 116*x^2 + 109*x + 74, x^95 + 15*x^93 + 122*x^92 + 101*x^91 + 20*x^90 + 35*x^89 + 30*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 26*x^84 + 25*x^83 + 12*x^82 + 127*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 3*x^75 + 124*x^74 + 85*x^73 + 34*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 118*x^68 + 39*x^67 + 36*x^66 + 97*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 89*x^27 + 36*x^26 + 79*x^25 + 22*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 66*x^20 + 61*x^19 + 124*x^18 + 59*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 39*x^11 + 12*x^10 + 81*x^9 + 122*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 126*x^4 + 27*x^3 + 20*x^2 + 77*x + 90, x^95 + 15*x^93 + 78*x^92 + 85*x^91 + 124*x^90 + 19*x^89 + 90*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 110*x^84 + 105*x^83 + 100*x^82 + 79*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 83*x^75 + 52*x^74 + 37*x^73 + 102*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 66*x^68 + 23*x^67 + 44*x^66 + 81*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 9*x^27 + 44*x^26 + 127*x^25 + 66*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 102*x^20 + 77*x^19 + 52*x^18 + 75*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 55*x^11 + 100*x^10 + 97*x^9 + 110*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 90*x^4 + 75*x^3 + 124*x^2 + 125*x + 78, x^95 + 15*x^93 + 50*x^92 + 53*x^91 + 36*x^90 + 51*x^89 + 6*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 82*x^84 + 9*x^83 + 124*x^82 + 47*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 115*x^75 + 44*x^74 + 5*x^73 + 58*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 126*x^68 + 119*x^67 + 116*x^66 + 113*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 105*x^27 + 116*x^26 + 31*x^25 + 30*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 90*x^20 + 109*x^19 + 44*x^18 + 43*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 87*x^11 + 124*x^10 + 65*x^9 + 50*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 102*x^4 + 43*x^3 + 36*x^2 + 29*x + 18, x^95 + 15*x^93 + 46*x^92 + 117*x^91 + 92*x^90 + 115*x^89 + 90*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 14*x^84 + 73*x^83 + 4*x^82 + 111*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 51*x^75 + 84*x^74 + 69*x^73 + 102*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 34*x^68 + 55*x^67 + 12*x^66 + 49*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 41*x^27 + 12*x^26 + 95*x^25 + 66*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 6*x^20 + 45*x^19 + 84*x^18 + 107*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 23*x^11 + 4*x^10 + x^9 + 110*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 58*x^4 + 107*x^3 + 92*x^2 + 93*x + 14, x^95 + 15*x^93 + 62*x^92 + 85*x^91 + 124*x^90 + 19*x^89 + 10*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 30*x^84 + 105*x^83 + 100*x^82 + 79*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 83*x^75 + 52*x^74 + 37*x^73 + 54*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 18*x^68 + 23*x^67 + 44*x^66 + 81*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 9*x^27 + 44*x^26 + 127*x^25 + 50*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 86*x^20 + 77*x^19 + 52*x^18 + 75*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 55*x^11 + 100*x^10 + 97*x^9 + 126*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 106*x^4 + 75*x^3 + 124*x^2 + 125*x + 30, x^95 + 15*x^93 + 22*x^92 + 53*x^91 + 60*x^90 + 19*x^89 + 98*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 86*x^84 + 9*x^83 + 100*x^82 + 79*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 115*x^75 + 116*x^74 + 37*x^73 + 30*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 90*x^68 + 119*x^67 + 44*x^66 + 81*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 105*x^27 + 108*x^26 + 127*x^25 + 106*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 110*x^20 + 109*x^19 + 52*x^18 + 75*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 87*x^11 + 36*x^10 + 97*x^9 + 70*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 18*x^4 + 43*x^3 + 124*x^2 + 125*x + 70, x^95 + 15*x^93 + 54*x^92 + 21*x^91 + 60*x^90 + 115*x^89 + 66*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 118*x^84 + 41*x^83 + 100*x^82 + 111*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 19*x^75 + 116*x^74 + 69*x^73 + 62*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 58*x^68 + 87*x^67 + 44*x^66 + 49*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 73*x^27 + 108*x^26 + 95*x^25 + 74*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 14*x^20 + 13*x^19 + 52*x^18 + 107*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 119*x^11 + 36*x^10 + x^9 + 102*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 114*x^4 + 11*x^3 + 124*x^2 + 93*x + 102, x^95 + 15*x^93 + 14*x^92 + 37*x^91 + 76*x^90 + 67*x^89 + 10*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 78*x^84 + 89*x^83 + 84*x^82 + 95*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 67*x^75 + 36*x^74 + 53*x^73 + 118*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 34*x^68 + 103*x^67 + 124*x^66 + x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 25*x^27 + 60*x^26 + 111*x^25 + 50*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 70*x^20 + 125*x^19 + 100*x^18 + 27*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 103*x^11 + 20*x^10 + 49*x^9 + 62*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 58*x^4 + 91*x^3 + 12*x^2 + 109*x + 62, x^95 + 15*x^93 + 42*x^92 + 5*x^91 + 52*x^90 + 3*x^89 + 110*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 74*x^84 + 121*x^83 + 108*x^82 + 31*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 99*x^75 + 92*x^74 + 117*x^73 + 82*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 70*x^68 + 71*x^67 + 68*x^66 + 65*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 121*x^27 + 68*x^26 + 47*x^25 + 38*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 50*x^20 + 29*x^19 + 92*x^18 + 91*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 7*x^11 + 108*x^10 + 113*x^9 + 106*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 14*x^4 + 59*x^3 + 52*x^2 + 45*x + 74, x^95 + 15*x^93 + 118*x^92 + 117*x^91 + 60*x^90 + 19*x^89 + 2*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 54*x^84 + 73*x^83 + 100*x^82 + 79*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 51*x^75 + 116*x^74 + 37*x^73 + 126*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 122*x^68 + 55*x^67 + 44*x^66 + 81*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 41*x^27 + 108*x^26 + 127*x^25 + 10*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 78*x^20 + 45*x^19 + 52*x^18 + 75*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 23*x^11 + 36*x^10 + 97*x^9 + 38*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 50*x^4 + 107*x^3 + 124*x^2 + 125*x + 38, x^95 + 15*x^93 + 10*x^92 + 21*x^91 + 36*x^90 + 115*x^89 + 30*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 10*x^84 + 41*x^83 + 60*x^82 + 111*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 19*x^75 + 44*x^74 + 69*x^73 + 98*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 70*x^68 + 87*x^67 + 52*x^66 + 49*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 73*x^27 + 116*x^26 + 95*x^25 + 22*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 114*x^20 + 13*x^19 + 108*x^18 + 107*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 119*x^11 + 124*x^10 + x^9 + 58*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 14*x^4 + 11*x^3 + 100*x^2 + 93*x + 122, x^95 + 15*x^93 + 34*x^92 + 85*x^91 + 100*x^90 + 83*x^89 + 54*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 2*x^84 + 105*x^83 + 60*x^82 + 15*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 83*x^75 + 108*x^74 + 101*x^73 + 10*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 78*x^68 + 23*x^67 + 52*x^66 + 17*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 9*x^27 + 52*x^26 + 63*x^25 + 14*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 74*x^20 + 77*x^19 + 108*x^18 + 11*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 55*x^11 + 60*x^10 + 33*x^9 + 66*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 118*x^4 + 75*x^3 + 100*x^2 + 61*x + 98, x^95 + 15*x^93 + 54*x^92 + 117*x^91 + 124*x^90 + 83*x^89 + 66*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 118*x^84 + 73*x^83 + 36*x^82 + 15*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 51*x^75 + 52*x^74 + 101*x^73 + 62*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 58*x^68 + 55*x^67 + 108*x^66 + 17*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 41*x^27 + 44*x^26 + 63*x^25 + 74*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 14*x^20 + 45*x^19 + 116*x^18 + 11*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 23*x^11 + 100*x^10 + 33*x^9 + 102*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 114*x^4 + 107*x^3 + 60*x^2 + 61*x + 102, x^95 + 15*x^93 + 54*x^92 + 37*x^91 + 12*x^90 + 35*x^89 + 114*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 22*x^84 + 89*x^83 + 84*x^82 + 127*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 67*x^75 + 100*x^74 + 85*x^73 + 78*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 90*x^68 + 103*x^67 + 124*x^66 + 97*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 25*x^27 + 124*x^26 + 79*x^25 + 58*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 46*x^20 + 125*x^19 + 100*x^18 + 59*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 103*x^11 + 84*x^10 + 81*x^9 + 54*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 18*x^4 + 91*x^3 + 12*x^2 + 77*x + 86, x^95 + 15*x^93 + 110*x^92 + 21*x^91 + 124*x^90 + 83*x^89 + 122*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 14*x^84 + 41*x^83 + 100*x^82 + 15*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 19*x^75 + 52*x^74 + 101*x^73 + 70*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 34*x^68 + 87*x^67 + 44*x^66 + 17*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 73*x^27 + 44*x^26 + 63*x^25 + 98*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 6*x^20 + 13*x^19 + 52*x^18 + 11*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 119*x^11 + 100*x^10 + 33*x^9 + 78*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 58*x^4 + 11*x^3 + 124*x^2 + 61*x + 46, x^95 + 15*x^93 + 58*x^92 + 117*x^91 + 68*x^90 + 83*x^89 + 46*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 58*x^84 + 73*x^83 + 28*x^82 + 15*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 51*x^75 + 12*x^74 + 101*x^73 + 82*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 22*x^68 + 55*x^67 + 84*x^66 + 17*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 41*x^27 + 20*x^26 + 63*x^25 + 102*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 98*x^20 + 45*x^19 + 76*x^18 + 11*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 23*x^11 + 92*x^10 + 33*x^9 + 106*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 30*x^4 + 107*x^3 + 4*x^2 + 61*x + 42, x^95 + 15*x^93 + 6*x^92 + 85*x^91 + 92*x^90 + 115*x^89 + 114*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 70*x^84 + 105*x^83 + 68*x^82 + 111*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 83*x^75 + 84*x^74 + 69*x^73 + 14*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 106*x^68 + 23*x^67 + 76*x^66 + 49*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 9*x^27 + 12*x^26 + 95*x^25 + 58*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 30*x^20 + 77*x^19 + 20*x^18 + 107*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 55*x^11 + 4*x^10 + x^9 + 118*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 98*x^4 + 75*x^3 + 28*x^2 + 93*x + 118, x^95 + 15*x^93 + 18*x^92 + 53*x^91 + 36*x^90 + 51*x^89 + 102*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 50*x^84 + 9*x^83 + 124*x^82 + 47*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 115*x^75 + 44*x^74 + 5*x^73 + 90*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 30*x^68 + 119*x^67 + 116*x^66 + 113*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 105*x^27 + 116*x^26 + 31*x^25 + 126*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 58*x^20 + 109*x^19 + 44*x^18 + 43*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 87*x^11 + 124*x^10 + 65*x^9 + 82*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 6*x^4 + 43*x^3 + 36*x^2 + 29*x + 50, x^95 + 15*x^93 + 122*x^92 + 5*x^91 + 20*x^90 + 67*x^89 + 94*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 26*x^84 + 121*x^83 + 12*x^82 + 95*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 99*x^75 + 124*x^74 + 53*x^73 + 98*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 118*x^68 + 71*x^67 + 36*x^66 + x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 121*x^27 + 36*x^26 + 111*x^25 + 86*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 66*x^20 + 29*x^19 + 124*x^18 + 27*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 7*x^11 + 12*x^10 + 49*x^9 + 58*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 126*x^4 + 59*x^3 + 20*x^2 + 109*x + 26, x^95 + 15*x^93 + 18*x^92 + 101*x^91 + 116*x^90 + 67*x^89 + 22*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 82*x^84 + 25*x^83 + 108*x^82 + 95*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 3*x^75 + 28*x^74 + 53*x^73 + 106*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 62*x^68 + 39*x^67 + 68*x^66 + x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 89*x^27 + 4*x^26 + 111*x^25 + 110*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 90*x^20 + 61*x^19 + 92*x^18 + 27*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 39*x^11 + 44*x^10 + 49*x^9 + 34*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 38*x^4 + 27*x^3 + 52*x^2 + 109*x + 34, x^95 + 15*x^93 + 98*x^92 + 69*x^91 + 20*x^90 + 99*x^89 + 6*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 34*x^84 + 57*x^83 + 76*x^82 + 63*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 35*x^75 + 124*x^74 + 21*x^73 + 122*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 110*x^68 + 7*x^67 + 100*x^66 + 33*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 57*x^27 + 36*x^26 + 15*x^25 + 30*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 106*x^20 + 93*x^19 + 60*x^18 + 123*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 71*x^11 + 12*x^10 + 17*x^9 + 114*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 22*x^4 + 123*x^3 + 84*x^2 + 13*x + 114, x^95 + 15*x^93 + 94*x^92 + 53*x^91 + 124*x^90 + 115*x^89 + 106*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 62*x^84 + 9*x^83 + 100*x^82 + 111*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 115*x^75 + 52*x^74 + 69*x^73 + 86*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 114*x^68 + 119*x^67 + 44*x^66 + 49*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 105*x^27 + 44*x^26 + 95*x^25 + 18*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 118*x^20 + 109*x^19 + 52*x^18 + 107*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 87*x^11 + 100*x^10 + x^9 + 30*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 74*x^4 + 43*x^3 + 124*x^2 + 93*x + 62, x^95 + 15*x^93 + 74*x^92 + 21*x^91 + 4*x^90 + 115*x^89 + 126*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 10*x^84 + 41*x^83 + 92*x^82 + 111*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 19*x^75 + 76*x^74 + 69*x^73 + 2*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 70*x^68 + 87*x^67 + 20*x^66 + 49*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 73*x^27 + 84*x^26 + 95*x^25 + 118*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 114*x^20 + 13*x^19 + 12*x^18 + 107*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 119*x^11 + 28*x^10 + x^9 + 90*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 14*x^4 + 11*x^3 + 68*x^2 + 93*x + 90, x^95 + 15*x^93 + 114*x^92 + 69*x^91 + 84*x^90 + 99*x^89 + 22*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 114*x^84 + 57*x^83 + 12*x^82 + 63*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 35*x^75 + 60*x^74 + 21*x^73 + 106*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 30*x^68 + 7*x^67 + 36*x^66 + 33*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 57*x^27 + 100*x^26 + 15*x^25 + 110*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 122*x^20 + 93*x^19 + 124*x^18 + 123*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 71*x^11 + 76*x^10 + 17*x^9 + 34*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 6*x^4 + 123*x^3 + 20*x^2 + 13*x + 98, x^95 + 15*x^93 + 86*x^92 + 69*x^91 + 76*x^90 + 67*x^89 + 18*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 54*x^84 + 57*x^83 + 20*x^82 + 95*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 35*x^75 + 36*x^74 + 53*x^73 + 46*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 58*x^68 + 7*x^67 + 60*x^66 + x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 57*x^27 + 60*x^26 + 111*x^25 + 90*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 78*x^20 + 93*x^19 + 36*x^18 + 27*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 71*x^11 + 20*x^10 + 49*x^9 + 22*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 114*x^4 + 123*x^3 + 76*x^2 + 109*x + 54, x^95 + 15*x^93 + 50*x^92 + 5*x^91 + 20*x^90 + 35*x^89 + 22*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 50*x^84 + 121*x^83 + 76*x^82 + 127*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 99*x^75 + 124*x^74 + 85*x^73 + 106*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 94*x^68 + 71*x^67 + 100*x^66 + 97*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 121*x^27 + 36*x^26 + 79*x^25 + 110*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 58*x^20 + 29*x^19 + 60*x^18 + 59*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 7*x^11 + 12*x^10 + 81*x^9 + 34*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 70*x^4 + 59*x^3 + 84*x^2 + 77*x + 98, x^95 + 15*x^93 + 118*x^92 + 85*x^91 + 124*x^90 + 115*x^89 + 2*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 54*x^84 + 105*x^83 + 36*x^82 + 111*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 83*x^75 + 52*x^74 + 69*x^73 + 126*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 122*x^68 + 23*x^67 + 108*x^66 + 49*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 9*x^27 + 44*x^26 + 95*x^25 + 10*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 78*x^20 + 77*x^19 + 116*x^18 + 107*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 55*x^11 + 100*x^10 + x^9 + 38*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 50*x^4 + 75*x^3 + 60*x^2 + 93*x + 38, x^95 + 15*x^93 + 90*x^92 + 21*x^91 + 68*x^90 + 51*x^89 + 78*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 90*x^84 + 41*x^83 + 28*x^82 + 47*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 19*x^75 + 12*x^74 + 5*x^73 + 50*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 118*x^68 + 87*x^67 + 84*x^66 + 113*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 73*x^27 + 20*x^26 + 31*x^25 + 6*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 2*x^20 + 13*x^19 + 76*x^18 + 43*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 119*x^11 + 92*x^10 + 65*x^9 + 74*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 126*x^4 + 11*x^3 + 4*x^2 + 29*x + 10, x^95 + 15*x^93 + 106*x^92 + 69*x^91 + 20*x^90 + 67*x^89 + 78*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 74*x^84 + 57*x^83 + 12*x^82 + 95*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 35*x^75 + 124*x^74 + 53*x^73 + 114*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 70*x^68 + 7*x^67 + 36*x^66 + x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 57*x^27 + 36*x^26 + 111*x^25 + 6*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 50*x^20 + 93*x^19 + 124*x^18 + 27*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 71*x^11 + 12*x^10 + 49*x^9 + 10*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 14*x^4 + 123*x^3 + 20*x^2 + 109*x + 42, x^95 + 15*x^93 + 18*x^92 + 21*x^91 + 4*x^90 + 19*x^89 + 70*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 114*x^84 + 41*x^83 + 28*x^82 + 79*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 19*x^75 + 76*x^74 + 37*x^73 + 122*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 94*x^68 + 87*x^67 + 84*x^66 + 81*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 73*x^27 + 84*x^26 + 127*x^25 + 94*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 122*x^20 + 13*x^19 + 76*x^18 + 75*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 119*x^11 + 28*x^10 + 97*x^9 + 114*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 70*x^4 + 11*x^3 + 4*x^2 + 125*x + 18, x^95 + 15*x^93 + 90*x^92 + 53*x^91 + 100*x^90 + 83*x^89 + 110*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 26*x^84 + 9*x^83 + 124*x^82 + 15*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 115*x^75 + 108*x^74 + 101*x^73 + 18*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 54*x^68 + 119*x^67 + 116*x^66 + 17*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 105*x^27 + 52*x^26 + 63*x^25 + 38*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 66*x^20 + 109*x^19 + 44*x^18 + 11*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 87*x^11 + 60*x^10 + 33*x^9 + 42*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 62*x^4 + 43*x^3 + 36*x^2 + 61*x + 42, x^95 + 15*x^93 + 122*x^92 + 101*x^91 + 20*x^90 + 99*x^89 + 94*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 26*x^84 + 25*x^83 + 12*x^82 + 63*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 3*x^75 + 124*x^74 + 21*x^73 + 98*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 118*x^68 + 39*x^67 + 36*x^66 + 33*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 89*x^27 + 36*x^26 + 15*x^25 + 86*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 66*x^20 + 61*x^19 + 124*x^18 + 123*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 39*x^11 + 12*x^10 + 17*x^9 + 58*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 126*x^4 + 27*x^3 + 20*x^2 + 13*x + 26, x^95 + 15*x^93 + 26*x^92 + 101*x^91 + 84*x^90 + 99*x^89 + 62*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 58*x^84 + 25*x^83 + 76*x^82 + 63*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 3*x^75 + 60*x^74 + 21*x^73 + 2*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 86*x^68 + 39*x^67 + 100*x^66 + 33*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 89*x^27 + 100*x^26 + 15*x^25 + 54*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 98*x^20 + 61*x^19 + 60*x^18 + 123*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 39*x^11 + 76*x^10 + 17*x^9 + 90*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 94*x^4 + 27*x^3 + 84*x^2 + 13*x + 58, x^95 + 15*x^93 + 106*x^92 + 37*x^91 + 84*x^90 + 99*x^89 + 14*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 74*x^84 + 89*x^83 + 76*x^82 + 63*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 67*x^75 + 60*x^74 + 21*x^73 + 50*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 70*x^68 + 103*x^67 + 100*x^66 + 33*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 25*x^27 + 100*x^26 + 15*x^25 + 70*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 50*x^20 + 125*x^19 + 60*x^18 + 123*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 103*x^11 + 76*x^10 + 17*x^9 + 74*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 14*x^4 + 91*x^3 + 84*x^2 + 13*x + 106, x^95 + 15*x^93 + 70*x^92 + 69*x^91 + 12*x^90 + 3*x^89 + 66*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 102*x^84 + 57*x^83 + 84*x^82 + 31*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 35*x^75 + 100*x^74 + 117*x^73 + 126*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 10*x^68 + 7*x^67 + 124*x^66 + 65*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 57*x^27 + 124*x^26 + 47*x^25 + 74*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 62*x^20 + 93*x^19 + 100*x^18 + 91*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 71*x^11 + 84*x^10 + 113*x^9 + 38*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 2*x^4 + 123*x^3 + 12*x^2 + 45*x + 6, x^95 + 15*x^93 + 22*x^92 + 85*x^91 + 60*x^90 + 51*x^89 + 34*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 86*x^84 + 105*x^83 + 100*x^82 + 47*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 83*x^75 + 116*x^74 + 5*x^73 + 94*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 90*x^68 + 23*x^67 + 44*x^66 + 113*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 9*x^27 + 108*x^26 + 31*x^25 + 42*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 110*x^20 + 77*x^19 + 52*x^18 + 43*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 55*x^11 + 36*x^10 + 65*x^9 + 6*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 18*x^4 + 75*x^3 + 124*x^2 + 29*x + 6, x^95 + 15*x^93 + 94*x^92 + 117*x^91 + 60*x^90 + 115*x^89 + 106*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 62*x^84 + 73*x^83 + 36*x^82 + 111*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 51*x^75 + 116*x^74 + 69*x^73 + 86*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 114*x^68 + 55*x^67 + 108*x^66 + 49*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 41*x^27 + 108*x^26 + 95*x^25 + 18*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 118*x^20 + 45*x^19 + 116*x^18 + 107*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 23*x^11 + 36*x^10 + x^9 + 30*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 74*x^4 + 107*x^3 + 60*x^2 + 93*x + 62, x^95 + 15*x^93 + 10*x^92 + 37*x^91 + 20*x^90 + 35*x^89 + 46*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 106*x^84 + 89*x^83 + 12*x^82 + 127*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 67*x^75 + 124*x^74 + 85*x^73 + 18*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 38*x^68 + 103*x^67 + 36*x^66 + 97*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 25*x^27 + 36*x^26 + 79*x^25 + 102*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 82*x^20 + 125*x^19 + 124*x^18 + 59*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 103*x^11 + 12*x^10 + 81*x^9 + 42*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 110*x^4 + 91*x^3 + 20*x^2 + 77*x + 74, x^95 + 15*x^93 + 6*x^92 + 21*x^91 + 92*x^90 + 51*x^89 + 114*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 70*x^84 + 41*x^83 + 68*x^82 + 47*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 19*x^75 + 84*x^74 + 5*x^73 + 14*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 106*x^68 + 87*x^67 + 76*x^66 + 113*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 73*x^27 + 12*x^26 + 31*x^25 + 58*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 30*x^20 + 13*x^19 + 20*x^18 + 43*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 119*x^11 + 4*x^10 + 65*x^9 + 118*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 98*x^4 + 11*x^3 + 28*x^2 + 29*x + 118, x^95 + 15*x^93 + 74*x^92 + 21*x^91 + 4*x^90 + 51*x^89 + 62*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 10*x^84 + 41*x^83 + 92*x^82 + 47*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 19*x^75 + 76*x^74 + 5*x^73 + 66*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 70*x^68 + 87*x^67 + 20*x^66 + 113*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 73*x^27 + 84*x^26 + 31*x^25 + 54*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 114*x^20 + 13*x^19 + 12*x^18 + 43*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 119*x^11 + 28*x^10 + 65*x^9 + 26*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 14*x^4 + 11*x^3 + 68*x^2 + 29*x + 26, x^95 + 15*x^93 + 78*x^92 + 5*x^91 + 108*x^90 + 35*x^89 + 106*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 78*x^84 + 121*x^83 + 52*x^82 + 127*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 99*x^75 + 4*x^74 + 85*x^73 + 22*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 34*x^68 + 71*x^67 + 28*x^66 + 97*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 121*x^27 + 92*x^26 + 79*x^25 + 18*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 70*x^20 + 29*x^19 + 68*x^18 + 59*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 7*x^11 + 116*x^10 + 81*x^9 + 94*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 58*x^4 + 59*x^3 + 44*x^2 + 77*x + 30, x^95 + 15*x^93 + 58*x^92 + 117*x^91 + 100*x^90 + 19*x^89 + 78*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 122*x^84 + 73*x^83 + 124*x^82 + 79*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 51*x^75 + 108*x^74 + 37*x^73 + 50*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 86*x^68 + 55*x^67 + 116*x^66 + 81*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 41*x^27 + 52*x^26 + 127*x^25 + 6*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 34*x^20 + 45*x^19 + 44*x^18 + 75*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 23*x^11 + 60*x^10 + 97*x^9 + 74*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 94*x^4 + 107*x^3 + 36*x^2 + 125*x + 74, x^95 + 15*x^93 + 30*x^92 + 69*x^91 + 76*x^90 + 99*x^89 + 26*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 30*x^84 + 57*x^83 + 84*x^82 + 63*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 35*x^75 + 36*x^74 + 21*x^73 + 102*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 82*x^68 + 7*x^67 + 124*x^66 + 33*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 57*x^27 + 60*x^26 + 15*x^25 + 2*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 86*x^20 + 93*x^19 + 100*x^18 + 123*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 71*x^11 + 20*x^10 + 17*x^9 + 110*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 42*x^4 + 123*x^3 + 12*x^2 + 13*x + 46, x^95 + 15*x^93 + 34*x^92 + 69*x^91 + 116*x^90 + 99*x^89 + 102*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 34*x^84 + 57*x^83 + 108*x^82 + 63*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 35*x^75 + 28*x^74 + 21*x^73 + 26*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 110*x^68 + 7*x^67 + 68*x^66 + 33*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 57*x^27 + 4*x^26 + 15*x^25 + 126*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 106*x^20 + 93*x^19 + 92*x^18 + 123*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 71*x^11 + 44*x^10 + 17*x^9 + 18*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 22*x^4 + 123*x^3 + 52*x^2 + 13*x + 82, x^95 + 15*x^93 + 114*x^92 + 37*x^91 + 84*x^90 + 67*x^89 + 86*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 114*x^84 + 89*x^83 + 12*x^82 + 95*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 67*x^75 + 60*x^74 + 53*x^73 + 42*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 30*x^68 + 103*x^67 + 36*x^66 + x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 25*x^27 + 100*x^26 + 111*x^25 + 46*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 122*x^20 + 125*x^19 + 124*x^18 + 27*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 103*x^11 + 76*x^10 + 49*x^9 + 98*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 6*x^4 + 91*x^3 + 20*x^2 + 109*x + 34, x^95 + 15*x^93 + 90*x^92 + 85*x^91 + 4*x^90 + 51*x^89 + 78*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 90*x^84 + 105*x^83 + 92*x^82 + 47*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 83*x^75 + 76*x^74 + 5*x^73 + 50*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 118*x^68 + 23*x^67 + 20*x^66 + 113*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 9*x^27 + 84*x^26 + 31*x^25 + 6*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 2*x^20 + 77*x^19 + 12*x^18 + 43*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 55*x^11 + 28*x^10 + 65*x^9 + 74*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 126*x^4 + 75*x^3 + 68*x^2 + 29*x + 10, x^95 + 15*x^93 + 22*x^92 + 101*x^91 + 44*x^90 + 99*x^89 + 50*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 54*x^84 + 25*x^83 + 52*x^82 + 63*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 3*x^75 + 68*x^74 + 21*x^73 + 14*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 58*x^68 + 39*x^67 + 28*x^66 + 33*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 89*x^27 + 28*x^26 + 15*x^25 + 122*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 78*x^20 + 61*x^19 + 68*x^18 + 123*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 39*x^11 + 52*x^10 + 17*x^9 + 118*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 114*x^4 + 27*x^3 + 44*x^2 + 13*x + 86, x^95 + 15*x^93 + 82*x^92 + 53*x^91 + 4*x^90 + 115*x^89 + 6*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 50*x^84 + 9*x^83 + 28*x^82 + 111*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 115*x^75 + 76*x^74 + 69*x^73 + 58*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 30*x^68 + 119*x^67 + 84*x^66 + 49*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 105*x^27 + 84*x^26 + 95*x^25 + 30*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 58*x^20 + 109*x^19 + 76*x^18 + 107*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 87*x^11 + 28*x^10 + x^9 + 50*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 6*x^4 + 43*x^3 + 4*x^2 + 93*x + 82, x^95 + 15*x^93 + 110*x^92 + 53*x^91 + 28*x^90 + 115*x^89 + 26*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 78*x^84 + 9*x^83 + 68*x^82 + 111*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 115*x^75 + 20*x^74 + 69*x^73 + 38*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 98*x^68 + 119*x^67 + 76*x^66 + 49*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 105*x^27 + 76*x^26 + 95*x^25 + 2*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 70*x^20 + 109*x^19 + 20*x^18 + 107*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 87*x^11 + 68*x^10 + x^9 + 46*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 122*x^4 + 43*x^3 + 28*x^2 + 93*x + 78, x^95 + 15*x^93 + 126*x^92 + 85*x^91 + 60*x^90 + 83*x^89 + 74*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 94*x^84 + 105*x^83 + 36*x^82 + 15*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 83*x^75 + 116*x^74 + 101*x^73 + 118*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 82*x^68 + 23*x^67 + 108*x^66 + 17*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 9*x^27 + 108*x^26 + 63*x^25 + 114*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 22*x^20 + 77*x^19 + 116*x^18 + 11*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 55*x^11 + 36*x^10 + 33*x^9 + 62*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 42*x^4 + 75*x^3 + 60*x^2 + 61*x + 94, x^95 + 15*x^93 + 74*x^92 + 37*x^91 + 52*x^90 + 99*x^89 + 14*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 106*x^84 + 89*x^83 + 108*x^82 + 63*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 67*x^75 + 92*x^74 + 21*x^73 + 50*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 38*x^68 + 103*x^67 + 68*x^66 + 33*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 25*x^27 + 68*x^26 + 15*x^25 + 70*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 82*x^20 + 125*x^19 + 92*x^18 + 123*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 103*x^11 + 108*x^10 + 17*x^9 + 74*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 110*x^4 + 91*x^3 + 52*x^2 + 13*x + 42, x^95 + 15*x^93 + 74*x^92 + 21*x^91 + 68*x^90 + 115*x^89 + 62*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 10*x^84 + 41*x^83 + 28*x^82 + 111*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 19*x^75 + 12*x^74 + 69*x^73 + 66*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 70*x^68 + 87*x^67 + 84*x^66 + 49*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 73*x^27 + 20*x^26 + 95*x^25 + 54*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 114*x^20 + 13*x^19 + 76*x^18 + 107*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 119*x^11 + 92*x^10 + x^9 + 26*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 14*x^4 + 11*x^3 + 4*x^2 + 93*x + 26, x^95 + 15*x^93 + 94*x^92 + 37*x^91 + 44*x^90 + 67*x^89 + 58*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 30*x^84 + 89*x^83 + 116*x^82 + 95*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 67*x^75 + 68*x^74 + 53*x^73 + 70*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 82*x^68 + 103*x^67 + 92*x^66 + x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 25*x^27 + 28*x^26 + 111*x^25 + 34*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 86*x^20 + 125*x^19 + 4*x^18 + 27*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 103*x^11 + 52*x^10 + 49*x^9 + 78*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 42*x^4 + 91*x^3 + 108*x^2 + 109*x + 78, x^95 + 15*x^93 + 50*x^92 + 69*x^91 + 52*x^90 + 99*x^89 + 118*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 114*x^84 + 57*x^83 + 44*x^82 + 63*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 35*x^75 + 92*x^74 + 21*x^73 + 10*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 30*x^68 + 7*x^67 + 4*x^66 + 33*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 57*x^27 + 68*x^26 + 15*x^25 + 78*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 122*x^20 + 93*x^19 + 28*x^18 + 123*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 71*x^11 + 108*x^10 + 17*x^9 + 66*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 6*x^4 + 123*x^3 + 116*x^2 + 13*x + 66, x^95 + 15*x^93 + 102*x^92 + 101*x^91 + 44*x^90 + 35*x^89 + 2*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 70*x^84 + 25*x^83 + 52*x^82 + 127*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 3*x^75 + 68*x^74 + 85*x^73 + 62*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 42*x^68 + 39*x^67 + 28*x^66 + 97*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 89*x^27 + 28*x^26 + 79*x^25 + 10*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 30*x^20 + 61*x^19 + 68*x^18 + 59*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 39*x^11 + 52*x^10 + 81*x^9 + 102*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 34*x^4 + 27*x^3 + 44*x^2 + 77*x + 6, x^95 + 15*x^93 + 74*x^92 + 37*x^91 + 20*x^90 + 35*x^89 + 110*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 42*x^84 + 89*x^83 + 12*x^82 + 127*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 67*x^75 + 124*x^74 + 85*x^73 + 82*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 102*x^68 + 103*x^67 + 36*x^66 + 97*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 25*x^27 + 36*x^26 + 79*x^25 + 38*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 18*x^20 + 125*x^19 + 124*x^18 + 59*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 103*x^11 + 12*x^10 + 81*x^9 + 106*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 46*x^4 + 91*x^3 + 20*x^2 + 77*x + 10, x^95 + 15*x^93 + 26*x^92 + 37*x^91 + 20*x^90 + 35*x^89 + 126*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 58*x^84 + 89*x^83 + 12*x^82 + 127*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 67*x^75 + 124*x^74 + 85*x^73 + 66*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 86*x^68 + 103*x^67 + 36*x^66 + 97*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 25*x^27 + 36*x^26 + 79*x^25 + 118*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 98*x^20 + 125*x^19 + 124*x^18 + 59*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 103*x^11 + 12*x^10 + 81*x^9 + 26*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 94*x^4 + 91*x^3 + 20*x^2 + 77*x + 122, x^95 + 15*x^93 + 114*x^92 + 117*x^91 + 4*x^90 + 51*x^89 + 38*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 82*x^84 + 73*x^83 + 28*x^82 + 47*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 51*x^75 + 76*x^74 + 5*x^73 + 26*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 126*x^68 + 55*x^67 + 84*x^66 + 113*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 41*x^27 + 84*x^26 + 31*x^25 + 62*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 90*x^20 + 45*x^19 + 76*x^18 + 43*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 23*x^11 + 28*x^10 + 65*x^9 + 18*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 102*x^4 + 107*x^3 + 4*x^2 + 29*x + 50, x^95 + 15*x^93 + 106*x^92 + 101*x^91 + 52*x^90 + 99*x^89 + 110*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 10*x^84 + 25*x^83 + 108*x^82 + 63*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 3*x^75 + 92*x^74 + 21*x^73 + 82*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 6*x^68 + 39*x^67 + 68*x^66 + 33*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 89*x^27 + 68*x^26 + 15*x^25 + 38*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 114*x^20 + 61*x^19 + 92*x^18 + 123*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 39*x^11 + 108*x^10 + 17*x^9 + 106*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 78*x^4 + 27*x^3 + 52*x^2 + 13*x + 74, x^95 + 15*x^93 + 82*x^92 + 5*x^91 + 20*x^90 + 99*x^89 + 118*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 82*x^84 + 121*x^83 + 76*x^82 + 63*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 99*x^75 + 124*x^74 + 21*x^73 + 10*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 62*x^68 + 71*x^67 + 100*x^66 + 33*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 121*x^27 + 36*x^26 + 15*x^25 + 78*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 90*x^20 + 29*x^19 + 60*x^18 + 123*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 7*x^11 + 12*x^10 + 17*x^9 + 66*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 38*x^4 + 59*x^3 + 84*x^2 + 13*x + 2, x^95 + 15*x^93 + 50*x^92 + 85*x^91 + 68*x^90 + 19*x^89 + 102*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 18*x^84 + 105*x^83 + 92*x^82 + 79*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 83*x^75 + 12*x^74 + 37*x^73 + 90*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 62*x^68 + 23*x^67 + 20*x^66 + 81*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 9*x^27 + 20*x^26 + 127*x^25 + 126*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 26*x^20 + 77*x^19 + 12*x^18 + 75*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 55*x^11 + 92*x^10 + 97*x^9 + 82*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 38*x^4 + 75*x^3 + 68*x^2 + 125*x + 114, x^95 + 15*x^93 + 42*x^92 + 85*x^91 + 68*x^90 + 115*x^89 + 94*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 106*x^84 + 105*x^83 + 28*x^82 + 111*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 83*x^75 + 12*x^74 + 69*x^73 + 34*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 102*x^68 + 23*x^67 + 84*x^66 + 49*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 9*x^27 + 20*x^26 + 95*x^25 + 86*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 82*x^20 + 77*x^19 + 76*x^18 + 107*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 55*x^11 + 92*x^10 + x^9 + 122*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 46*x^4 + 75*x^3 + 4*x^2 + 93*x + 122, x^95 + 15*x^93 + 94*x^92 + 117*x^91 + 28*x^90 + 115*x^89 + 10*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 126*x^84 + 73*x^83 + 68*x^82 + 111*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 51*x^75 + 20*x^74 + 69*x^73 + 54*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 50*x^68 + 55*x^67 + 76*x^66 + 49*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 41*x^27 + 76*x^26 + 95*x^25 + 50*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 54*x^20 + 45*x^19 + 20*x^18 + 107*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 23*x^11 + 68*x^10 + x^9 + 126*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 10*x^4 + 107*x^3 + 28*x^2 + 93*x + 94, x^95 + 15*x^93 + 30*x^92 + 85*x^91 + 92*x^90 + 19*x^89 + 10*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 62*x^84 + 105*x^83 + 4*x^82 + 79*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 83*x^75 + 84*x^74 + 37*x^73 + 54*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 114*x^68 + 23*x^67 + 12*x^66 + 81*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 9*x^27 + 12*x^26 + 127*x^25 + 50*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 118*x^20 + 77*x^19 + 84*x^18 + 75*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 55*x^11 + 4*x^10 + 97*x^9 + 126*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 74*x^4 + 75*x^3 + 92*x^2 + 125*x + 94, x^95 + 15*x^93 + 42*x^92 + 53*x^91 + 68*x^90 + 83*x^89 + 30*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 106*x^84 + 9*x^83 + 28*x^82 + 15*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 115*x^75 + 12*x^74 + 101*x^73 + 98*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 102*x^68 + 119*x^67 + 84*x^66 + 17*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 105*x^27 + 20*x^26 + 63*x^25 + 22*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 82*x^20 + 109*x^19 + 76*x^18 + 11*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 87*x^11 + 92*x^10 + 33*x^9 + 58*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 46*x^4 + 43*x^3 + 4*x^2 + 61*x + 58, x^95 + 15*x^93 + 66*x^92 + 37*x^91 + 20*x^90 + 3*x^89 + 102*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 2*x^84 + 89*x^83 + 76*x^82 + 31*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 67*x^75 + 124*x^74 + 117*x^73 + 26*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 14*x^68 + 103*x^67 + 100*x^66 + 65*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 25*x^27 + 36*x^26 + 47*x^25 + 126*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 74*x^20 + 125*x^19 + 60*x^18 + 91*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 103*x^11 + 12*x^10 + 113*x^9 + 18*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 54*x^4 + 91*x^3 + 84*x^2 + 45*x + 18, x^95 + 15*x^93 + 86*x^92 + 53*x^91 + 124*x^90 + 83*x^89 + 34*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 22*x^84 + 9*x^83 + 36*x^82 + 15*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 115*x^75 + 52*x^74 + 101*x^73 + 94*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 26*x^68 + 119*x^67 + 108*x^66 + 17*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 105*x^27 + 44*x^26 + 63*x^25 + 42*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 46*x^20 + 109*x^19 + 116*x^18 + 11*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 87*x^11 + 100*x^10 + 33*x^9 + 6*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 82*x^4 + 43*x^3 + 60*x^2 + 61*x + 6, x^95 + 15*x^93 + 2*x^92 + 101*x^91 + 52*x^90 + 67*x^89 + 6*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 2*x^84 + 25*x^83 + 44*x^82 + 95*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 3*x^75 + 92*x^74 + 53*x^73 + 122*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 14*x^68 + 39*x^67 + 4*x^66 + x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 89*x^27 + 68*x^26 + 111*x^25 + 30*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 74*x^20 + 61*x^19 + 28*x^18 + 27*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 39*x^11 + 108*x^10 + 49*x^9 + 114*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 54*x^4 + 27*x^3 + 116*x^2 + 109*x + 50, x^95 + 15*x^93 + 26*x^92 + 37*x^91 + 116*x^90 + 99*x^89 + 94*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 122*x^84 + 89*x^83 + 44*x^82 + 63*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 67*x^75 + 28*x^74 + 21*x^73 + 98*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 22*x^68 + 103*x^67 + 4*x^66 + 33*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 25*x^27 + 4*x^26 + 15*x^25 + 86*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 34*x^20 + 125*x^19 + 28*x^18 + 123*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 103*x^11 + 44*x^10 + 17*x^9 + 58*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 30*x^4 + 91*x^3 + 116*x^2 + 13*x + 90, x^95 + 15*x^93 + 42*x^92 + 101*x^91 + 84*x^90 + 99*x^89 + 14*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 10*x^84 + 25*x^83 + 76*x^82 + 63*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 3*x^75 + 60*x^74 + 21*x^73 + 50*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 6*x^68 + 39*x^67 + 100*x^66 + 33*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 89*x^27 + 100*x^26 + 15*x^25 + 70*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 114*x^20 + 61*x^19 + 60*x^18 + 123*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 39*x^11 + 76*x^10 + 17*x^9 + 74*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 78*x^4 + 27*x^3 + 84*x^2 + 13*x + 106, x^95 + 15*x^93 + 106*x^92 + 53*x^91 + 68*x^90 + 19*x^89 + 30*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 42*x^84 + 9*x^83 + 28*x^82 + 79*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 115*x^75 + 12*x^74 + 37*x^73 + 98*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 38*x^68 + 119*x^67 + 84*x^66 + 81*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 105*x^27 + 20*x^26 + 127*x^25 + 22*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 18*x^20 + 109*x^19 + 76*x^18 + 75*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 87*x^11 + 92*x^10 + 97*x^9 + 58*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 110*x^4 + 43*x^3 + 4*x^2 + 125*x + 58, x^95 + 15*x^93 + 90*x^92 + 101*x^91 + 20*x^90 + 35*x^89 + 126*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 122*x^84 + 25*x^83 + 12*x^82 + 127*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 3*x^75 + 124*x^74 + 85*x^73 + 66*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 22*x^68 + 39*x^67 + 36*x^66 + 97*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 89*x^27 + 36*x^26 + 79*x^25 + 118*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 34*x^20 + 61*x^19 + 124*x^18 + 59*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 39*x^11 + 12*x^10 + 81*x^9 + 26*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 30*x^4 + 27*x^3 + 20*x^2 + 77*x + 122, x^95 + 15*x^93 + 2*x^92 + 37*x^91 + 116*x^90 + 67*x^89 + 6*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 2*x^84 + 89*x^83 + 108*x^82 + 95*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 67*x^75 + 28*x^74 + 53*x^73 + 122*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 14*x^68 + 103*x^67 + 68*x^66 + x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 25*x^27 + 4*x^26 + 111*x^25 + 30*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 74*x^20 + 125*x^19 + 92*x^18 + 27*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 103*x^11 + 44*x^10 + 49*x^9 + 114*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 54*x^4 + 91*x^3 + 52*x^2 + 109*x + 50, x^95 + 15*x^93 + 78*x^92 + 21*x^91 + 92*x^90 + 83*x^89 + 122*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 46*x^84 + 41*x^83 + 4*x^82 + 15*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 19*x^75 + 84*x^74 + 101*x^73 + 70*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 2*x^68 + 87*x^67 + 12*x^66 + 17*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 73*x^27 + 12*x^26 + 63*x^25 + 98*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 38*x^20 + 13*x^19 + 84*x^18 + 11*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 119*x^11 + 4*x^10 + 33*x^9 + 78*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 26*x^4 + 11*x^3 + 92*x^2 + 61*x + 110, x^95 + 15*x^93 + 54*x^92 + 117*x^91 + 124*x^90 + 19*x^89 + 2*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 118*x^84 + 73*x^83 + 36*x^82 + 79*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 51*x^75 + 52*x^74 + 37*x^73 + 126*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 58*x^68 + 55*x^67 + 108*x^66 + 81*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 41*x^27 + 44*x^26 + 127*x^25 + 10*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 14*x^20 + 45*x^19 + 116*x^18 + 75*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 23*x^11 + 100*x^10 + 97*x^9 + 38*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 114*x^4 + 107*x^3 + 60*x^2 + 125*x + 38, x^95 + 15*x^93 + 66*x^92 + 101*x^91 + 20*x^90 + 67*x^89 + 102*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 2*x^84 + 25*x^83 + 76*x^82 + 95*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 3*x^75 + 124*x^74 + 53*x^73 + 26*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 14*x^68 + 39*x^67 + 100*x^66 + x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 89*x^27 + 36*x^26 + 111*x^25 + 126*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 74*x^20 + 61*x^19 + 60*x^18 + 27*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 39*x^11 + 12*x^10 + 49*x^9 + 18*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 54*x^4 + 27*x^3 + 84*x^2 + 109*x + 18, x^95 + 15*x^93 + 82*x^92 + 69*x^91 + 52*x^90 + 35*x^89 + 86*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 18*x^84 + 57*x^83 + 44*x^82 + 127*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 35*x^75 + 92*x^74 + 85*x^73 + 42*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 126*x^68 + 7*x^67 + 4*x^66 + 97*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 57*x^27 + 68*x^26 + 79*x^25 + 46*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 26*x^20 + 93*x^19 + 28*x^18 + 59*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 71*x^11 + 108*x^10 + 81*x^9 + 98*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 102*x^4 + 123*x^3 + 116*x^2 + 77*x + 98, x^95 + 15*x^93 + 58*x^92 + 101*x^91 + 52*x^90 + 35*x^89 + 62*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 26*x^84 + 25*x^83 + 108*x^82 + 127*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 3*x^75 + 92*x^74 + 85*x^73 + 2*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 118*x^68 + 39*x^67 + 68*x^66 + 97*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 89*x^27 + 68*x^26 + 79*x^25 + 54*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 66*x^20 + 61*x^19 + 92*x^18 + 59*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 39*x^11 + 108*x^10 + 81*x^9 + 90*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 126*x^4 + 27*x^3 + 52*x^2 + 77*x + 122, x^95 + 15*x^93 + 74*x^92 + 5*x^91 + 52*x^90 + 3*x^89 + 14*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 106*x^84 + 121*x^83 + 108*x^82 + 31*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 99*x^75 + 92*x^74 + 117*x^73 + 50*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 38*x^68 + 71*x^67 + 68*x^66 + 65*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 121*x^27 + 68*x^26 + 47*x^25 + 70*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 82*x^20 + 29*x^19 + 92*x^18 + 91*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 7*x^11 + 108*x^10 + 113*x^9 + 74*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 110*x^4 + 59*x^3 + 52*x^2 + 45*x + 42, x^95 + 15*x^93 + 38*x^92 + 101*x^91 + 108*x^90 + 35*x^89 + 2*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 6*x^84 + 25*x^83 + 116*x^82 + 127*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 3*x^75 + 4*x^74 + 85*x^73 + 62*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 106*x^68 + 39*x^67 + 92*x^66 + 97*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 89*x^27 + 92*x^26 + 79*x^25 + 10*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 94*x^20 + 61*x^19 + 4*x^18 + 59*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 39*x^11 + 116*x^10 + 81*x^9 + 102*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 98*x^4 + 27*x^3 + 108*x^2 + 77*x + 6, x^95 + 15*x^93 + 6*x^92 + 69*x^91 + 44*x^90 + 67*x^89 + 34*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 102*x^84 + 57*x^83 + 52*x^82 + 95*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 35*x^75 + 68*x^74 + 53*x^73 + 30*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 10*x^68 + 7*x^67 + 28*x^66 + x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 57*x^27 + 28*x^26 + 111*x^25 + 42*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 62*x^20 + 93*x^19 + 68*x^18 + 27*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 71*x^11 + 52*x^10 + 49*x^9 + 70*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 2*x^4 + 123*x^3 + 44*x^2 + 109*x + 102, x^95 + 15*x^93 + 2*x^92 + 37*x^91 + 20*x^90 + 67*x^89 + 102*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 66*x^84 + 89*x^83 + 76*x^82 + 95*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 67*x^75 + 124*x^74 + 53*x^73 + 26*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 78*x^68 + 103*x^67 + 100*x^66 + x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 25*x^27 + 36*x^26 + 111*x^25 + 126*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 10*x^20 + 125*x^19 + 60*x^18 + 27*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 103*x^11 + 12*x^10 + 49*x^9 + 18*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 118*x^4 + 91*x^3 + 84*x^2 + 109*x + 18, x^95 + 15*x^93 + 126*x^92 + 5*x^91 + 108*x^90 + 35*x^89 + 90*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 62*x^84 + 121*x^83 + 52*x^82 + 127*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 99*x^75 + 4*x^74 + 85*x^73 + 38*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 50*x^68 + 71*x^67 + 28*x^66 + 97*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 121*x^27 + 92*x^26 + 79*x^25 + 66*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 118*x^20 + 29*x^19 + 68*x^18 + 59*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 7*x^11 + 116*x^10 + 81*x^9 + 46*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 10*x^4 + 59*x^3 + 44*x^2 + 77*x + 46, x^95 + 15*x^93 + 122*x^92 + 117*x^91 + 4*x^90 + 83*x^89 + 46*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 122*x^84 + 73*x^83 + 92*x^82 + 15*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 51*x^75 + 76*x^74 + 101*x^73 + 82*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 86*x^68 + 55*x^67 + 20*x^66 + 17*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 41*x^27 + 84*x^26 + 63*x^25 + 102*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 34*x^20 + 45*x^19 + 12*x^18 + 11*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 23*x^11 + 28*x^10 + 33*x^9 + 106*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 94*x^4 + 107*x^3 + 68*x^2 + 61*x + 42, x^95 + 15*x^93 + 102*x^92 + 37*x^91 + 12*x^90 + 99*x^89 + 34*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 6*x^84 + 89*x^83 + 84*x^82 + 63*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 67*x^75 + 100*x^74 + 21*x^73 + 30*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 106*x^68 + 103*x^67 + 124*x^66 + 33*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 25*x^27 + 124*x^26 + 15*x^25 + 42*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 94*x^20 + 125*x^19 + 100*x^18 + 123*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 103*x^11 + 84*x^10 + 17*x^9 + 70*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 98*x^4 + 91*x^3 + 12*x^2 + 13*x + 38, x^95 + 15*x^93 + 18*x^92 + 85*x^91 + 100*x^90 + 83*x^89 + 102*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 50*x^84 + 105*x^83 + 60*x^82 + 15*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 83*x^75 + 108*x^74 + 101*x^73 + 90*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 30*x^68 + 23*x^67 + 52*x^66 + 17*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 9*x^27 + 52*x^26 + 63*x^25 + 126*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 58*x^20 + 77*x^19 + 108*x^18 + 11*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 55*x^11 + 60*x^10 + 33*x^9 + 82*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 6*x^4 + 75*x^3 + 100*x^2 + 61*x + 50, x^95 + 15*x^93 + 10*x^92 + 53*x^91 + 4*x^90 + 83*x^89 + 62*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 74*x^84 + 9*x^83 + 92*x^82 + 15*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 115*x^75 + 76*x^74 + 101*x^73 + 66*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 6*x^68 + 119*x^67 + 20*x^66 + 17*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 105*x^27 + 84*x^26 + 63*x^25 + 54*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 50*x^20 + 109*x^19 + 12*x^18 + 11*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 87*x^11 + 28*x^10 + 33*x^9 + 26*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 78*x^4 + 43*x^3 + 68*x^2 + 61*x + 26, x^95 + 15*x^93 + 62*x^92 + 101*x^91 + 44*x^90 + 3*x^89 + 26*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 126*x^84 + 25*x^83 + 116*x^82 + 31*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 3*x^75 + 68*x^74 + 117*x^73 + 102*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 114*x^68 + 39*x^67 + 92*x^66 + 65*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 89*x^27 + 28*x^26 + 47*x^25 + 2*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 54*x^20 + 61*x^19 + 4*x^18 + 91*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 39*x^11 + 52*x^10 + 113*x^9 + 110*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 74*x^4 + 27*x^3 + 108*x^2 + 45*x + 110, x^95 + 15*x^93 + 98*x^92 + 53*x^91 + 36*x^90 + 51*x^89 + 118*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 66*x^84 + 9*x^83 + 124*x^82 + 47*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 115*x^75 + 44*x^74 + 5*x^73 + 74*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 14*x^68 + 119*x^67 + 116*x^66 + 113*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 105*x^27 + 116*x^26 + 31*x^25 + 78*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 10*x^20 + 109*x^19 + 44*x^18 + 43*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 87*x^11 + 124*x^10 + 65*x^9 + 2*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 54*x^4 + 43*x^3 + 36*x^2 + 29*x + 34, x^95 + 15*x^93 + 110*x^92 + 37*x^91 + 12*x^90 + 67*x^89 + 42*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 46*x^84 + 89*x^83 + 20*x^82 + 95*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 67*x^75 + 100*x^74 + 53*x^73 + 86*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 66*x^68 + 103*x^67 + 60*x^66 + x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 25*x^27 + 124*x^26 + 111*x^25 + 82*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 38*x^20 + 125*x^19 + 36*x^18 + 27*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 103*x^11 + 84*x^10 + 49*x^9 + 30*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 90*x^4 + 91*x^3 + 76*x^2 + 109*x + 30, x^95 + 15*x^93 + 58*x^92 + 37*x^91 + 52*x^90 + 99*x^89 + 62*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 26*x^84 + 89*x^83 + 108*x^82 + 63*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 67*x^75 + 92*x^74 + 21*x^73 + 2*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 118*x^68 + 103*x^67 + 68*x^66 + 33*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 25*x^27 + 68*x^26 + 15*x^25 + 54*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 66*x^20 + 125*x^19 + 92*x^18 + 123*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 103*x^11 + 108*x^10 + 17*x^9 + 90*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 126*x^4 + 91*x^3 + 52*x^2 + 13*x + 122, x^95 + 15*x^93 + 86*x^92 + 5*x^91 + 44*x^90 + 67*x^89 + 114*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 118*x^84 + 121*x^83 + 52*x^82 + 95*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 99*x^75 + 68*x^74 + 53*x^73 + 78*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 122*x^68 + 71*x^67 + 28*x^66 + x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 121*x^27 + 28*x^26 + 111*x^25 + 58*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 14*x^20 + 29*x^19 + 68*x^18 + 27*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 7*x^11 + 52*x^10 + 49*x^9 + 54*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 50*x^4 + 59*x^3 + 44*x^2 + 109*x + 22, x^95 + 15*x^93 + 94*x^92 + 37*x^91 + 76*x^90 + 67*x^89 + 26*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 94*x^84 + 89*x^83 + 84*x^82 + 95*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 67*x^75 + 36*x^74 + 53*x^73 + 102*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 18*x^68 + 103*x^67 + 124*x^66 + x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 25*x^27 + 60*x^26 + 111*x^25 + 2*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 22*x^20 + 125*x^19 + 100*x^18 + 27*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 103*x^11 + 20*x^10 + 49*x^9 + 110*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 106*x^4 + 91*x^3 + 12*x^2 + 109*x + 46, x^95 + 15*x^93 + 114*x^92 + 21*x^91 + 68*x^90 + 83*x^89 + 38*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 82*x^84 + 41*x^83 + 92*x^82 + 15*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 19*x^75 + 12*x^74 + 101*x^73 + 26*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 126*x^68 + 87*x^67 + 20*x^66 + 17*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 73*x^27 + 20*x^26 + 63*x^25 + 62*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 90*x^20 + 13*x^19 + 12*x^18 + 11*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 119*x^11 + 92*x^10 + 33*x^9 + 18*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 102*x^4 + 11*x^3 + 68*x^2 + 61*x + 50, x^95 + 15*x^93 + 26*x^92 + 5*x^91 + 116*x^90 + 3*x^89 + 94*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 122*x^84 + 121*x^83 + 44*x^82 + 31*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 99*x^75 + 28*x^74 + 117*x^73 + 98*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 22*x^68 + 71*x^67 + 4*x^66 + 65*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 121*x^27 + 4*x^26 + 47*x^25 + 86*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 34*x^20 + 29*x^19 + 28*x^18 + 91*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 7*x^11 + 44*x^10 + 113*x^9 + 58*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 30*x^4 + 59*x^3 + 116*x^2 + 45*x + 90, x^95 + 15*x^93 + 46*x^92 + 85*x^91 + 28*x^90 + 19*x^89 + 26*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 14*x^84 + 105*x^83 + 68*x^82 + 79*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 83*x^75 + 20*x^74 + 37*x^73 + 38*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 34*x^68 + 23*x^67 + 76*x^66 + 81*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 9*x^27 + 76*x^26 + 127*x^25 + 2*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 6*x^20 + 77*x^19 + 20*x^18 + 75*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 55*x^11 + 68*x^10 + 97*x^9 + 46*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 58*x^4 + 75*x^3 + 28*x^2 + 125*x + 78, x^95 + 15*x^93 + 14*x^92 + 85*x^91 + 124*x^90 + 19*x^89 + 26*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 46*x^84 + 105*x^83 + 100*x^82 + 79*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 83*x^75 + 52*x^74 + 37*x^73 + 38*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 2*x^68 + 23*x^67 + 44*x^66 + 81*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 9*x^27 + 44*x^26 + 127*x^25 + 2*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 38*x^20 + 77*x^19 + 52*x^18 + 75*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 55*x^11 + 100*x^10 + 97*x^9 + 46*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 26*x^4 + 75*x^3 + 124*x^2 + 125*x + 14, x^95 + 15*x^93 + 34*x^92 + 85*x^91 + 4*x^90 + 19*x^89 + 86*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 66*x^84 + 105*x^83 + 28*x^82 + 79*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 83*x^75 + 76*x^74 + 37*x^73 + 106*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 14*x^68 + 23*x^67 + 84*x^66 + 81*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 9*x^27 + 84*x^26 + 127*x^25 + 46*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 10*x^20 + 77*x^19 + 76*x^18 + 75*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 55*x^11 + 28*x^10 + 97*x^9 + 34*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 54*x^4 + 75*x^3 + 4*x^2 + 125*x + 2, x^95 + 15*x^93 + 82*x^92 + 117*x^91 + 36*x^90 + 51*x^89 + 102*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 114*x^84 + 73*x^83 + 124*x^82 + 47*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 51*x^75 + 44*x^74 + 5*x^73 + 90*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 94*x^68 + 55*x^67 + 116*x^66 + 113*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 41*x^27 + 116*x^26 + 31*x^25 + 126*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 122*x^20 + 45*x^19 + 44*x^18 + 43*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 23*x^11 + 124*x^10 + 65*x^9 + 82*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 70*x^4 + 107*x^3 + 36*x^2 + 29*x + 50, x^95 + 15*x^93 + 94*x^92 + 101*x^91 + 108*x^90 + 67*x^89 + 58*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 30*x^84 + 25*x^83 + 52*x^82 + 95*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 3*x^75 + 4*x^74 + 53*x^73 + 70*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 82*x^68 + 39*x^67 + 28*x^66 + x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 89*x^27 + 92*x^26 + 111*x^25 + 34*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 86*x^20 + 61*x^19 + 68*x^18 + 27*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 39*x^11 + 116*x^10 + 49*x^9 + 78*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 42*x^4 + 27*x^3 + 44*x^2 + 109*x + 78, x^95 + 15*x^93 + 14*x^92 + 37*x^91 + 44*x^90 + 67*x^89 + 42*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 14*x^84 + 89*x^83 + 116*x^82 + 95*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 67*x^75 + 68*x^74 + 53*x^73 + 86*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 98*x^68 + 103*x^67 + 92*x^66 + x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 25*x^27 + 28*x^26 + 111*x^25 + 82*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 6*x^20 + 125*x^19 + 4*x^18 + 27*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 103*x^11 + 52*x^10 + 49*x^9 + 30*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 122*x^4 + 91*x^3 + 108*x^2 + 109*x + 94, x^95 + 15*x^93 + 114*x^92 + 117*x^91 + 36*x^90 + 51*x^89 + 6*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 18*x^84 + 73*x^83 + 124*x^82 + 47*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 51*x^75 + 44*x^74 + 5*x^73 + 58*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 62*x^68 + 55*x^67 + 116*x^66 + 113*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 41*x^27 + 116*x^26 + 31*x^25 + 30*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 26*x^20 + 45*x^19 + 44*x^18 + 43*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 23*x^11 + 124*x^10 + 65*x^9 + 50*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 38*x^4 + 107*x^3 + 36*x^2 + 29*x + 18, x^95 + 15*x^93 + 42*x^92 + 117*x^91 + 36*x^90 + 83*x^89 + 126*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 42*x^84 + 73*x^83 + 60*x^82 + 15*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 51*x^75 + 44*x^74 + 101*x^73 + 2*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 38*x^68 + 55*x^67 + 52*x^66 + 17*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 41*x^27 + 116*x^26 + 63*x^25 + 118*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 18*x^20 + 45*x^19 + 108*x^18 + 11*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 23*x^11 + 124*x^10 + 33*x^9 + 90*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 110*x^4 + 107*x^3 + 100*x^2 + 61*x + 26, x^95 + 15*x^93 + 118*x^92 + 5*x^91 + 108*x^90 + 67*x^89 + 82*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 22*x^84 + 121*x^83 + 116*x^82 + 95*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 99*x^75 + 4*x^74 + 53*x^73 + 110*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 90*x^68 + 71*x^67 + 92*x^66 + x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 121*x^27 + 92*x^26 + 111*x^25 + 26*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 46*x^20 + 29*x^19 + 4*x^18 + 27*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 7*x^11 + 116*x^10 + 49*x^9 + 86*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 18*x^4 + 59*x^3 + 108*x^2 + 109*x + 54, x^95 + 15*x^93 + 74*x^92 + 69*x^91 + 52*x^90 + 67*x^89 + 14*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 106*x^84 + 57*x^83 + 108*x^82 + 95*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 35*x^75 + 92*x^74 + 53*x^73 + 50*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 38*x^68 + 7*x^67 + 68*x^66 + x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 57*x^27 + 68*x^26 + 111*x^25 + 70*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 82*x^20 + 93*x^19 + 92*x^18 + 27*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 71*x^11 + 108*x^10 + 49*x^9 + 74*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 110*x^4 + 123*x^3 + 52*x^2 + 109*x + 42, x^95 + 15*x^93 + 90*x^92 + 5*x^91 + 20*x^90 + 3*x^89 + 126*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 122*x^84 + 121*x^83 + 12*x^82 + 31*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 99*x^75 + 124*x^74 + 117*x^73 + 66*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 22*x^68 + 71*x^67 + 36*x^66 + 65*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 121*x^27 + 36*x^26 + 47*x^25 + 118*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 34*x^20 + 29*x^19 + 124*x^18 + 91*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 7*x^11 + 12*x^10 + 113*x^9 + 26*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 30*x^4 + 59*x^3 + 20*x^2 + 45*x + 122, x^95 + 15*x^93 + 78*x^92 + 101*x^91 + 108*x^90 + 3*x^89 + 42*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 78*x^84 + 25*x^83 + 52*x^82 + 31*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 3*x^75 + 4*x^74 + 117*x^73 + 86*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 34*x^68 + 39*x^67 + 28*x^66 + 65*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 89*x^27 + 92*x^26 + 47*x^25 + 82*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 70*x^20 + 61*x^19 + 68*x^18 + 91*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 39*x^11 + 116*x^10 + 113*x^9 + 30*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 58*x^4 + 27*x^3 + 44*x^2 + 45*x + 94, x^95 + 15*x^93 + 6*x^92 + 5*x^91 + 76*x^90 + 3*x^89 + 2*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 38*x^84 + 121*x^83 + 20*x^82 + 31*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 99*x^75 + 36*x^74 + 117*x^73 + 62*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 74*x^68 + 71*x^67 + 60*x^66 + 65*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 121*x^27 + 60*x^26 + 47*x^25 + 10*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 126*x^20 + 29*x^19 + 36*x^18 + 91*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 7*x^11 + 20*x^10 + 113*x^9 + 102*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 66*x^4 + 59*x^3 + 76*x^2 + 45*x + 70, x^95 + 15*x^93 + 86*x^92 + 21*x^91 + 28*x^90 + 51*x^89 + 66*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 86*x^84 + 41*x^83 + 4*x^82 + 47*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 19*x^75 + 20*x^74 + 5*x^73 + 62*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 90*x^68 + 87*x^67 + 12*x^66 + 113*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 73*x^27 + 76*x^26 + 31*x^25 + 74*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 110*x^20 + 13*x^19 + 84*x^18 + 43*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 119*x^11 + 68*x^10 + 65*x^9 + 102*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 18*x^4 + 11*x^3 + 92*x^2 + 29*x + 38, x^95 + 15*x^93 + 38*x^92 + 37*x^91 + 12*x^90 + 35*x^89 + 34*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 70*x^84 + 89*x^83 + 84*x^82 + 127*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 67*x^75 + 100*x^74 + 85*x^73 + 30*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 42*x^68 + 103*x^67 + 124*x^66 + 97*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 25*x^27 + 124*x^26 + 79*x^25 + 42*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 30*x^20 + 125*x^19 + 100*x^18 + 59*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 103*x^11 + 84*x^10 + 81*x^9 + 70*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 34*x^4 + 91*x^3 + 12*x^2 + 77*x + 38, x^95 + 15*x^93 + 10*x^92 + 37*x^91 + 84*x^90 + 35*x^89 + 110*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 106*x^84 + 89*x^83 + 76*x^82 + 127*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 67*x^75 + 60*x^74 + 85*x^73 + 82*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 38*x^68 + 103*x^67 + 100*x^66 + 97*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 25*x^27 + 100*x^26 + 79*x^25 + 38*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 82*x^20 + 125*x^19 + 60*x^18 + 59*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 103*x^11 + 76*x^10 + 81*x^9 + 106*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 110*x^4 + 91*x^3 + 84*x^2 + 77*x + 10, x^95 + 15*x^93 + 118*x^92 + 37*x^91 + 12*x^90 + 35*x^89 + 50*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 86*x^84 + 89*x^83 + 84*x^82 + 127*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 67*x^75 + 100*x^74 + 85*x^73 + 14*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 26*x^68 + 103*x^67 + 124*x^66 + 97*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 25*x^27 + 124*x^26 + 79*x^25 + 122*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 110*x^20 + 125*x^19 + 100*x^18 + 59*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 103*x^11 + 84*x^10 + 81*x^9 + 118*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 82*x^4 + 91*x^3 + 12*x^2 + 77*x + 22, x^95 + 15*x^93 + 102*x^92 + 5*x^91 + 12*x^90 + 3*x^89 + 34*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 6*x^84 + 121*x^83 + 84*x^82 + 31*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 99*x^75 + 100*x^74 + 117*x^73 + 30*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 106*x^68 + 71*x^67 + 124*x^66 + 65*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 121*x^27 + 124*x^26 + 47*x^25 + 42*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 94*x^20 + 29*x^19 + 100*x^18 + 91*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 7*x^11 + 84*x^10 + 113*x^9 + 70*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 98*x^4 + 59*x^3 + 12*x^2 + 45*x + 38, x^95 + 15*x^93 + 34*x^92 + 69*x^91 + 52*x^90 + 99*x^89 + 38*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 34*x^84 + 57*x^83 + 44*x^82 + 63*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 35*x^75 + 92*x^74 + 21*x^73 + 90*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 110*x^68 + 7*x^67 + 4*x^66 + 33*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 57*x^27 + 68*x^26 + 15*x^25 + 62*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 106*x^20 + 93*x^19 + 28*x^18 + 123*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 71*x^11 + 108*x^10 + 17*x^9 + 82*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 22*x^4 + 123*x^3 + 116*x^2 + 13*x + 18, x^95 + 15*x^93 + 14*x^92 + 5*x^91 + 108*x^90 + 99*x^89 + 106*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 14*x^84 + 121*x^83 + 52*x^82 + 63*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 99*x^75 + 4*x^74 + 21*x^73 + 22*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 98*x^68 + 71*x^67 + 28*x^66 + 33*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 121*x^27 + 92*x^26 + 15*x^25 + 18*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 6*x^20 + 29*x^19 + 68*x^18 + 123*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 7*x^11 + 116*x^10 + 17*x^9 + 94*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 122*x^4 + 59*x^3 + 44*x^2 + 13*x + 30, x^95 + 15*x^93 + 126*x^92 + 85*x^91 + 28*x^90 + 19*x^89 + 42*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 30*x^84 + 105*x^83 + 68*x^82 + 79*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 83*x^75 + 20*x^74 + 37*x^73 + 22*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 18*x^68 + 23*x^67 + 76*x^66 + 81*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 9*x^27 + 76*x^26 + 127*x^25 + 82*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 86*x^20 + 77*x^19 + 20*x^18 + 75*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 55*x^11 + 68*x^10 + 97*x^9 + 94*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 106*x^4 + 75*x^3 + 28*x^2 + 125*x + 62, x^95 + 15*x^93 + 122*x^92 + 5*x^91 + 84*x^90 + 67*x^89 + 30*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 26*x^84 + 121*x^83 + 76*x^82 + 95*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 99*x^75 + 60*x^74 + 53*x^73 + 34*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 118*x^68 + 71*x^67 + 100*x^66 + x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 121*x^27 + 100*x^26 + 111*x^25 + 22*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 66*x^20 + 29*x^19 + 60*x^18 + 27*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 7*x^11 + 76*x^10 + 49*x^9 + 122*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 126*x^4 + 59*x^3 + 84*x^2 + 109*x + 90, x^95 + 15*x^93 + 58*x^92 + 5*x^91 + 52*x^90 + 3*x^89 + 62*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 26*x^84 + 121*x^83 + 108*x^82 + 31*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 99*x^75 + 92*x^74 + 117*x^73 + 2*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 118*x^68 + 71*x^67 + 68*x^66 + 65*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 121*x^27 + 68*x^26 + 47*x^25 + 54*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 66*x^20 + 29*x^19 + 92*x^18 + 91*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 7*x^11 + 108*x^10 + 113*x^9 + 90*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 126*x^4 + 59*x^3 + 52*x^2 + 45*x + 122, x^95 + 15*x^93 + 54*x^92 + 53*x^91 + 92*x^90 + 83*x^89 + 34*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 54*x^84 + 9*x^83 + 68*x^82 + 15*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 115*x^75 + 84*x^74 + 101*x^73 + 94*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 122*x^68 + 119*x^67 + 76*x^66 + 17*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 105*x^27 + 12*x^26 + 63*x^25 + 42*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 78*x^20 + 109*x^19 + 20*x^18 + 11*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 87*x^11 + 4*x^10 + 33*x^9 + 6*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 50*x^4 + 43*x^3 + 28*x^2 + 61*x + 70, x^95 + 15*x^93 + 22*x^92 + 37*x^91 + 76*x^90 + 35*x^89 + 18*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 118*x^84 + 89*x^83 + 20*x^82 + 127*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 67*x^75 + 36*x^74 + 85*x^73 + 46*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 122*x^68 + 103*x^67 + 60*x^66 + 97*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 25*x^27 + 60*x^26 + 79*x^25 + 90*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 14*x^20 + 125*x^19 + 36*x^18 + 59*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 103*x^11 + 20*x^10 + 81*x^9 + 22*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 50*x^4 + 91*x^3 + 76*x^2 + 77*x + 54, x^95 + 15*x^93 + 2*x^92 + 37*x^91 + 84*x^90 + 3*x^89 + 102*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 66*x^84 + 89*x^83 + 12*x^82 + 31*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 67*x^75 + 60*x^74 + 117*x^73 + 26*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 78*x^68 + 103*x^67 + 36*x^66 + 65*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 25*x^27 + 100*x^26 + 47*x^25 + 126*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 10*x^20 + 125*x^19 + 124*x^18 + 91*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 103*x^11 + 76*x^10 + 113*x^9 + 18*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 118*x^4 + 91*x^3 + 20*x^2 + 45*x + 18, x^95 + 15*x^93 + 2*x^92 + 5*x^91 + 52*x^90 + 35*x^89 + 6*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 2*x^84 + 121*x^83 + 44*x^82 + 127*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 99*x^75 + 92*x^74 + 85*x^73 + 122*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 14*x^68 + 71*x^67 + 4*x^66 + 97*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 121*x^27 + 68*x^26 + 79*x^25 + 30*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 74*x^20 + 29*x^19 + 28*x^18 + 59*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 7*x^11 + 108*x^10 + 81*x^9 + 114*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 54*x^4 + 59*x^3 + 116*x^2 + 77*x + 50, x^95 + 15*x^93 + 98*x^92 + 53*x^91 + 68*x^90 + 51*x^89 + 86*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 2*x^84 + 9*x^83 + 92*x^82 + 47*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 115*x^75 + 12*x^74 + 5*x^73 + 106*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 78*x^68 + 119*x^67 + 20*x^66 + 113*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 105*x^27 + 20*x^26 + 31*x^25 + 46*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 74*x^20 + 109*x^19 + 12*x^18 + 43*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 87*x^11 + 92*x^10 + 65*x^9 + 34*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 118*x^4 + 43*x^3 + 68*x^2 + 29*x + 2, x^95 + 15*x^93 + 2*x^92 + 85*x^91 + 100*x^90 + 83*x^89 + 22*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 98*x^84 + 105*x^83 + 60*x^82 + 15*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 83*x^75 + 108*x^74 + 101*x^73 + 42*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 110*x^68 + 23*x^67 + 52*x^66 + 17*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 9*x^27 + 52*x^26 + 63*x^25 + 110*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 42*x^20 + 77*x^19 + 108*x^18 + 11*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 55*x^11 + 60*x^10 + 33*x^9 + 98*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 22*x^4 + 75*x^3 + 100*x^2 + 61*x + 2, x^95 + 15*x^93 + 78*x^92 + 117*x^91 + 124*x^90 + 51*x^89 + 26*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 110*x^84 + 73*x^83 + 100*x^82 + 47*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 51*x^75 + 52*x^74 + 5*x^73 + 38*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 66*x^68 + 55*x^67 + 44*x^66 + 113*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 41*x^27 + 44*x^26 + 31*x^25 + 2*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 102*x^20 + 45*x^19 + 52*x^18 + 43*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 23*x^11 + 100*x^10 + 65*x^9 + 46*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 90*x^4 + 107*x^3 + 124*x^2 + 29*x + 14, x^95 + 15*x^93 + 86*x^92 + 5*x^91 + 108*x^90 + 67*x^89 + 50*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 118*x^84 + 121*x^83 + 116*x^82 + 95*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 99*x^75 + 4*x^74 + 53*x^73 + 14*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 122*x^68 + 71*x^67 + 92*x^66 + x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 121*x^27 + 92*x^26 + 111*x^25 + 122*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 14*x^20 + 29*x^19 + 4*x^18 + 27*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 7*x^11 + 116*x^10 + 49*x^9 + 118*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 50*x^4 + 59*x^3 + 108*x^2 + 109*x + 86, x^95 + 15*x^93 + 82*x^92 + 69*x^91 + 84*x^90 + 99*x^89 + 118*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 82*x^84 + 57*x^83 + 12*x^82 + 63*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 35*x^75 + 60*x^74 + 21*x^73 + 10*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 62*x^68 + 7*x^67 + 36*x^66 + 33*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 57*x^27 + 100*x^26 + 15*x^25 + 78*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 90*x^20 + 93*x^19 + 124*x^18 + 123*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 71*x^11 + 76*x^10 + 17*x^9 + 66*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 38*x^4 + 123*x^3 + 20*x^2 + 13*x + 2, x^95 + 15*x^93 + 114*x^92 + 101*x^91 + 20*x^90 + 3*x^89 + 22*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 114*x^84 + 25*x^83 + 76*x^82 + 31*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 3*x^75 + 124*x^74 + 117*x^73 + 106*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 30*x^68 + 39*x^67 + 100*x^66 + 65*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 89*x^27 + 36*x^26 + 47*x^25 + 110*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 122*x^20 + 61*x^19 + 60*x^18 + 91*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 39*x^11 + 12*x^10 + 113*x^9 + 34*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 6*x^4 + 27*x^3 + 84*x^2 + 45*x + 98, x^95 + 15*x^93 + 50*x^92 + 85*x^91 + 36*x^90 + 19*x^89 + 6*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 82*x^84 + 105*x^83 + 124*x^82 + 79*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 83*x^75 + 44*x^74 + 37*x^73 + 58*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 126*x^68 + 23*x^67 + 116*x^66 + 81*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 9*x^27 + 116*x^26 + 127*x^25 + 30*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 90*x^20 + 77*x^19 + 44*x^18 + 75*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 55*x^11 + 124*x^10 + 97*x^9 + 50*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 102*x^4 + 75*x^3 + 36*x^2 + 125*x + 18, x^95 + 15*x^93 + 106*x^92 + 101*x^91 + 116*x^90 + 35*x^89 + 110*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 10*x^84 + 25*x^83 + 44*x^82 + 127*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 3*x^75 + 28*x^74 + 85*x^73 + 82*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 6*x^68 + 39*x^67 + 4*x^66 + 97*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 89*x^27 + 4*x^26 + 79*x^25 + 38*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 114*x^20 + 61*x^19 + 28*x^18 + 59*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 39*x^11 + 44*x^10 + 81*x^9 + 106*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 78*x^4 + 27*x^3 + 116*x^2 + 77*x + 74, x^95 + 15*x^93 + 98*x^92 + 5*x^91 + 52*x^90 + 99*x^89 + 38*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 98*x^84 + 121*x^83 + 44*x^82 + 63*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 99*x^75 + 92*x^74 + 21*x^73 + 90*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 46*x^68 + 71*x^67 + 4*x^66 + 33*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 121*x^27 + 68*x^26 + 15*x^25 + 62*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 42*x^20 + 29*x^19 + 28*x^18 + 123*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 7*x^11 + 108*x^10 + 17*x^9 + 82*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 86*x^4 + 59*x^3 + 116*x^2 + 13*x + 18, x^95 + 15*x^93 + 22*x^92 + 53*x^91 + 124*x^90 + 83*x^89 + 98*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 86*x^84 + 9*x^83 + 36*x^82 + 15*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 115*x^75 + 52*x^74 + 101*x^73 + 30*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 90*x^68 + 119*x^67 + 108*x^66 + 17*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 105*x^27 + 44*x^26 + 63*x^25 + 106*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 110*x^20 + 109*x^19 + 116*x^18 + 11*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 87*x^11 + 100*x^10 + 33*x^9 + 70*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 18*x^4 + 43*x^3 + 60*x^2 + 61*x + 70, x^95 + 15*x^93 + 2*x^92 + 101*x^91 + 84*x^90 + 67*x^89 + 102*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 66*x^84 + 25*x^83 + 12*x^82 + 95*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 3*x^75 + 60*x^74 + 53*x^73 + 26*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 78*x^68 + 39*x^67 + 36*x^66 + x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 89*x^27 + 100*x^26 + 111*x^25 + 126*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 10*x^20 + 61*x^19 + 124*x^18 + 27*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 39*x^11 + 76*x^10 + 49*x^9 + 18*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 118*x^4 + 27*x^3 + 20*x^2 + 109*x + 18, x^95 + 15*x^93 + 14*x^92 + 85*x^91 + 92*x^90 + 83*x^89 + 122*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 110*x^84 + 105*x^83 + 4*x^82 + 15*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 83*x^75 + 84*x^74 + 101*x^73 + 70*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 66*x^68 + 23*x^67 + 12*x^66 + 17*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 9*x^27 + 12*x^26 + 63*x^25 + 98*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 102*x^20 + 77*x^19 + 84*x^18 + 11*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 55*x^11 + 4*x^10 + 33*x^9 + 78*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 90*x^4 + 75*x^3 + 92*x^2 + 61*x + 110, x^95 + 15*x^93 + 14*x^92 + 69*x^91 + 76*x^90 + 35*x^89 + 10*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 78*x^84 + 57*x^83 + 84*x^82 + 127*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 35*x^75 + 36*x^74 + 85*x^73 + 118*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 34*x^68 + 7*x^67 + 124*x^66 + 97*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 57*x^27 + 60*x^26 + 79*x^25 + 50*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 70*x^20 + 93*x^19 + 100*x^18 + 59*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 71*x^11 + 20*x^10 + 81*x^9 + 62*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 58*x^4 + 123*x^3 + 12*x^2 + 77*x + 62, x^95 + 15*x^93 + 22*x^92 + 85*x^91 + 28*x^90 + 51*x^89 + 66*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 22*x^84 + 105*x^83 + 4*x^82 + 47*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 83*x^75 + 20*x^74 + 5*x^73 + 62*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 26*x^68 + 23*x^67 + 12*x^66 + 113*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 9*x^27 + 76*x^26 + 31*x^25 + 74*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 46*x^20 + 77*x^19 + 84*x^18 + 43*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 55*x^11 + 68*x^10 + 65*x^9 + 102*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 82*x^4 + 75*x^3 + 92*x^2 + 29*x + 38, x^95 + 15*x^93 + 70*x^92 + 69*x^91 + 44*x^90 + 67*x^89 + 98*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 38*x^84 + 57*x^83 + 52*x^82 + 95*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 35*x^75 + 68*x^74 + 53*x^73 + 94*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 74*x^68 + 7*x^67 + 28*x^66 + x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 57*x^27 + 28*x^26 + 111*x^25 + 106*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 126*x^20 + 93*x^19 + 68*x^18 + 27*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 71*x^11 + 52*x^10 + 49*x^9 + 6*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 66*x^4 + 123*x^3 + 44*x^2 + 109*x + 38, x^95 + 15*x^93 + 26*x^92 + 69*x^91 + 116*x^90 + 67*x^89 + 94*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 122*x^84 + 57*x^83 + 44*x^82 + 95*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 35*x^75 + 28*x^74 + 53*x^73 + 98*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 22*x^68 + 7*x^67 + 4*x^66 + x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 57*x^27 + 4*x^26 + 111*x^25 + 86*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 34*x^20 + 93*x^19 + 28*x^18 + 27*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 71*x^11 + 44*x^10 + 49*x^9 + 58*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 30*x^4 + 123*x^3 + 116*x^2 + 109*x + 90, x^95 + 15*x^93 + 62*x^92 + 21*x^91 + 124*x^90 + 83*x^89 + 10*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 30*x^84 + 41*x^83 + 100*x^82 + 15*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 19*x^75 + 52*x^74 + 101*x^73 + 54*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 18*x^68 + 87*x^67 + 44*x^66 + 17*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 73*x^27 + 44*x^26 + 63*x^25 + 50*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 86*x^20 + 13*x^19 + 52*x^18 + 11*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 119*x^11 + 100*x^10 + 33*x^9 + 126*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 106*x^4 + 11*x^3 + 124*x^2 + 61*x + 30, x^95 + 15*x^93 + 94*x^92 + 21*x^91 + 92*x^90 + 19*x^89 + 10*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 126*x^84 + 41*x^83 + 4*x^82 + 79*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 19*x^75 + 84*x^74 + 37*x^73 + 54*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 50*x^68 + 87*x^67 + 12*x^66 + 81*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 73*x^27 + 12*x^26 + 127*x^25 + 50*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 54*x^20 + 13*x^19 + 84*x^18 + 75*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 119*x^11 + 4*x^10 + 97*x^9 + 126*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 10*x^4 + 11*x^3 + 92*x^2 + 125*x + 94, x^95 + 15*x^93 + 18*x^92 + 85*x^91 + 36*x^90 + 19*x^89 + 102*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 50*x^84 + 105*x^83 + 124*x^82 + 79*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 83*x^75 + 44*x^74 + 37*x^73 + 90*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 30*x^68 + 23*x^67 + 116*x^66 + 81*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 9*x^27 + 116*x^26 + 127*x^25 + 126*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 58*x^20 + 77*x^19 + 44*x^18 + 75*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 55*x^11 + 124*x^10 + 97*x^9 + 82*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 6*x^4 + 75*x^3 + 36*x^2 + 125*x + 50, x^95 + 15*x^93 + 126*x^92 + 117*x^91 + 124*x^90 + 115*x^89 + 74*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 94*x^84 + 73*x^83 + 100*x^82 + 111*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 51*x^75 + 52*x^74 + 69*x^73 + 118*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 82*x^68 + 55*x^67 + 44*x^66 + 49*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 41*x^27 + 44*x^26 + 95*x^25 + 114*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 22*x^20 + 45*x^19 + 52*x^18 + 107*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 23*x^11 + 100*x^10 + x^9 + 62*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 42*x^4 + 107*x^3 + 124*x^2 + 93*x + 94, x^95 + 15*x^93 + 118*x^92 + 53*x^91 + 92*x^90 + 83*x^89 + 98*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 118*x^84 + 9*x^83 + 68*x^82 + 15*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 115*x^75 + 84*x^74 + 101*x^73 + 30*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 58*x^68 + 119*x^67 + 76*x^66 + 17*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 105*x^27 + 12*x^26 + 63*x^25 + 106*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 14*x^20 + 109*x^19 + 20*x^18 + 11*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 87*x^11 + 4*x^10 + 33*x^9 + 70*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 114*x^4 + 43*x^3 + 28*x^2 + 61*x + 6, x^95 + 15*x^93 + 42*x^92 + 53*x^91 + 36*x^90 + 19*x^89 + 126*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 42*x^84 + 9*x^83 + 60*x^82 + 79*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 115*x^75 + 44*x^74 + 37*x^73 + 2*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 38*x^68 + 119*x^67 + 52*x^66 + 81*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 105*x^27 + 116*x^26 + 127*x^25 + 118*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 18*x^20 + 109*x^19 + 108*x^18 + 75*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 87*x^11 + 124*x^10 + 97*x^9 + 90*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 110*x^4 + 43*x^3 + 100*x^2 + 125*x + 26, x^95 + 15*x^93 + 6*x^92 + 101*x^91 + 12*x^90 + 35*x^89 + 66*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 38*x^84 + 25*x^83 + 84*x^82 + 127*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 3*x^75 + 100*x^74 + 85*x^73 + 126*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 74*x^68 + 39*x^67 + 124*x^66 + 97*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 89*x^27 + 124*x^26 + 79*x^25 + 74*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 126*x^20 + 61*x^19 + 100*x^18 + 59*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 39*x^11 + 84*x^10 + 81*x^9 + 38*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 66*x^4 + 27*x^3 + 12*x^2 + 77*x + 6, x^95 + 15*x^93 + 74*x^92 + 21*x^91 + 36*x^90 + 51*x^89 + 30*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 74*x^84 + 41*x^83 + 60*x^82 + 47*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 19*x^75 + 44*x^74 + 5*x^73 + 98*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 6*x^68 + 87*x^67 + 52*x^66 + 113*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 73*x^27 + 116*x^26 + 31*x^25 + 22*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 50*x^20 + 13*x^19 + 108*x^18 + 43*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 119*x^11 + 124*x^10 + 65*x^9 + 58*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 78*x^4 + 11*x^3 + 100*x^2 + 29*x + 122, x^95 + 15*x^93 + 58*x^92 + 69*x^91 + 52*x^90 + 67*x^89 + 62*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 26*x^84 + 57*x^83 + 108*x^82 + 95*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 35*x^75 + 92*x^74 + 53*x^73 + 2*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 118*x^68 + 7*x^67 + 68*x^66 + x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 57*x^27 + 68*x^26 + 111*x^25 + 54*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 66*x^20 + 93*x^19 + 92*x^18 + 27*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 71*x^11 + 108*x^10 + 49*x^9 + 90*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 126*x^4 + 123*x^3 + 52*x^2 + 109*x + 122, x^95 + 15*x^93 + 22*x^92 + 101*x^91 + 44*x^90 + 35*x^89 + 114*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 54*x^84 + 25*x^83 + 52*x^82 + 127*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 3*x^75 + 68*x^74 + 85*x^73 + 78*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 58*x^68 + 39*x^67 + 28*x^66 + 97*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 89*x^27 + 28*x^26 + 79*x^25 + 58*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 78*x^20 + 61*x^19 + 68*x^18 + 59*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 39*x^11 + 52*x^10 + 81*x^9 + 54*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 114*x^4 + 27*x^3 + 44*x^2 + 77*x + 22, x^95 + 15*x^93 + 114*x^92 + 85*x^91 + 100*x^90 + 19*x^89 + 6*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 18*x^84 + 105*x^83 + 60*x^82 + 79*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 83*x^75 + 108*x^74 + 37*x^73 + 58*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 62*x^68 + 23*x^67 + 52*x^66 + 81*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 9*x^27 + 52*x^26 + 127*x^25 + 30*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 26*x^20 + 77*x^19 + 108*x^18 + 75*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 55*x^11 + 60*x^10 + 97*x^9 + 50*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 38*x^4 + 75*x^3 + 100*x^2 + 125*x + 18, x^95 + 15*x^93 + 98*x^92 + 21*x^91 + 68*x^90 + 83*x^89 + 86*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 2*x^84 + 41*x^83 + 92*x^82 + 15*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 19*x^75 + 12*x^74 + 101*x^73 + 106*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 78*x^68 + 87*x^67 + 20*x^66 + 17*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 73*x^27 + 20*x^26 + 63*x^25 + 46*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 74*x^20 + 13*x^19 + 12*x^18 + 11*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 119*x^11 + 92*x^10 + 33*x^9 + 34*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 118*x^4 + 11*x^3 + 68*x^2 + 61*x + 2, x^95 + 15*x^93 + 6*x^92 + 21*x^91 + 28*x^90 + 51*x^89 + 50*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 70*x^84 + 41*x^83 + 4*x^82 + 47*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 19*x^75 + 20*x^74 + 5*x^73 + 78*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 106*x^68 + 87*x^67 + 12*x^66 + 113*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 73*x^27 + 76*x^26 + 31*x^25 + 122*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 30*x^20 + 13*x^19 + 84*x^18 + 43*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 119*x^11 + 68*x^10 + 65*x^9 + 54*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 98*x^4 + 11*x^3 + 92*x^2 + 29*x + 54, x^95 + 15*x^93 + 114*x^92 + 53*x^91 + 36*x^90 + 115*x^89 + 6*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 18*x^84 + 9*x^83 + 124*x^82 + 111*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 115*x^75 + 44*x^74 + 69*x^73 + 58*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 62*x^68 + 119*x^67 + 116*x^66 + 49*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 105*x^27 + 116*x^26 + 95*x^25 + 30*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 26*x^20 + 109*x^19 + 44*x^18 + 107*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 87*x^11 + 124*x^10 + x^9 + 50*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 38*x^4 + 43*x^3 + 36*x^2 + 93*x + 18, x^95 + 15*x^93 + 50*x^92 + 21*x^91 + 36*x^90 + 83*x^89 + 6*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 82*x^84 + 41*x^83 + 124*x^82 + 15*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 19*x^75 + 44*x^74 + 101*x^73 + 58*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 126*x^68 + 87*x^67 + 116*x^66 + 17*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 73*x^27 + 116*x^26 + 63*x^25 + 30*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 90*x^20 + 13*x^19 + 44*x^18 + 11*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 119*x^11 + 124*x^10 + 33*x^9 + 50*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 102*x^4 + 11*x^3 + 36*x^2 + 61*x + 18, x^95 + 15*x^93 + 14*x^92 + 101*x^91 + 108*x^90 + 67*x^89 + 42*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 14*x^84 + 25*x^83 + 52*x^82 + 95*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 3*x^75 + 4*x^74 + 53*x^73 + 86*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 98*x^68 + 39*x^67 + 28*x^66 + x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 89*x^27 + 92*x^26 + 111*x^25 + 82*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 6*x^20 + 61*x^19 + 68*x^18 + 27*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 39*x^11 + 116*x^10 + 49*x^9 + 30*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 122*x^4 + 27*x^3 + 44*x^2 + 109*x + 94, x^95 + 15*x^93 + 26*x^92 + 117*x^91 + 68*x^90 + 19*x^89 + 78*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 26*x^84 + 73*x^83 + 28*x^82 + 79*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 51*x^75 + 12*x^74 + 37*x^73 + 50*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 54*x^68 + 55*x^67 + 84*x^66 + 81*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 41*x^27 + 20*x^26 + 127*x^25 + 6*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 66*x^20 + 45*x^19 + 76*x^18 + 75*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 23*x^11 + 92*x^10 + 97*x^9 + 74*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 62*x^4 + 107*x^3 + 4*x^2 + 125*x + 10, x^95 + 15*x^93 + 74*x^92 + 37*x^91 + 116*x^90 + 35*x^89 + 14*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 106*x^84 + 89*x^83 + 44*x^82 + 127*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 67*x^75 + 28*x^74 + 85*x^73 + 50*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 38*x^68 + 103*x^67 + 4*x^66 + 97*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 25*x^27 + 4*x^26 + 79*x^25 + 70*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 82*x^20 + 125*x^19 + 28*x^18 + 59*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 103*x^11 + 44*x^10 + 81*x^9 + 74*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 110*x^4 + 91*x^3 + 116*x^2 + 77*x + 42, x^95 + 15*x^93 + 18*x^92 + 21*x^91 + 4*x^90 + 83*x^89 + 6*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 114*x^84 + 41*x^83 + 28*x^82 + 15*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 19*x^75 + 76*x^74 + 101*x^73 + 58*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 94*x^68 + 87*x^67 + 84*x^66 + 17*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 73*x^27 + 84*x^26 + 63*x^25 + 30*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 122*x^20 + 13*x^19 + 76*x^18 + 11*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 119*x^11 + 28*x^10 + 33*x^9 + 50*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 70*x^4 + 11*x^3 + 4*x^2 + 61*x + 82, x^95 + 15*x^93 + 6*x^92 + 101*x^91 + 12*x^90 + 99*x^89 + 2*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 38*x^84 + 25*x^83 + 84*x^82 + 63*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 3*x^75 + 100*x^74 + 21*x^73 + 62*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 74*x^68 + 39*x^67 + 124*x^66 + 33*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 89*x^27 + 124*x^26 + 15*x^25 + 10*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 126*x^20 + 61*x^19 + 100*x^18 + 123*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 39*x^11 + 84*x^10 + 17*x^9 + 102*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 66*x^4 + 27*x^3 + 12*x^2 + 13*x + 70, x^95 + 15*x^93 + 54*x^92 + 5*x^91 + 108*x^90 + 67*x^89 + 18*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 86*x^84 + 121*x^83 + 116*x^82 + 95*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 99*x^75 + 4*x^74 + 53*x^73 + 46*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 26*x^68 + 71*x^67 + 92*x^66 + x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 121*x^27 + 92*x^26 + 111*x^25 + 90*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 110*x^20 + 29*x^19 + 4*x^18 + 27*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 7*x^11 + 116*x^10 + 49*x^9 + 22*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 82*x^4 + 59*x^3 + 108*x^2 + 109*x + 118, x^95 + 15*x^93 + 10*x^92 + 101*x^91 + 52*x^90 + 35*x^89 + 78*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 42*x^84 + 25*x^83 + 108*x^82 + 127*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 3*x^75 + 92*x^74 + 85*x^73 + 114*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 102*x^68 + 39*x^67 + 68*x^66 + 97*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 89*x^27 + 68*x^26 + 79*x^25 + 6*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 18*x^20 + 61*x^19 + 92*x^18 + 59*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 39*x^11 + 108*x^10 + 81*x^9 + 10*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 46*x^4 + 27*x^3 + 52*x^2 + 77*x + 106, x^95 + 15*x^93 + 98*x^92 + 117*x^91 + 36*x^90 + 115*x^89 + 118*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 66*x^84 + 73*x^83 + 124*x^82 + 111*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 51*x^75 + 44*x^74 + 69*x^73 + 74*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 14*x^68 + 55*x^67 + 116*x^66 + 49*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 41*x^27 + 116*x^26 + 95*x^25 + 78*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 10*x^20 + 45*x^19 + 44*x^18 + 107*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 23*x^11 + 124*x^10 + x^9 + 2*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 54*x^4 + 107*x^3 + 36*x^2 + 93*x + 34, x^95 + 15*x^93 + 6*x^92 + 37*x^91 + 12*x^90 + 99*x^89 + 66*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 38*x^84 + 89*x^83 + 84*x^82 + 63*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 67*x^75 + 100*x^74 + 21*x^73 + 126*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 74*x^68 + 103*x^67 + 124*x^66 + 33*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 25*x^27 + 124*x^26 + 15*x^25 + 74*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 126*x^20 + 125*x^19 + 100*x^18 + 123*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 103*x^11 + 84*x^10 + 17*x^9 + 38*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 66*x^4 + 91*x^3 + 12*x^2 + 13*x + 6, x^95 + 15*x^93 + 58*x^92 + 85*x^91 + 100*x^90 + 51*x^89 + 78*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 122*x^84 + 105*x^83 + 124*x^82 + 47*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 83*x^75 + 108*x^74 + 5*x^73 + 50*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 86*x^68 + 23*x^67 + 116*x^66 + 113*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 9*x^27 + 52*x^26 + 31*x^25 + 6*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 34*x^20 + 77*x^19 + 44*x^18 + 43*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 55*x^11 + 60*x^10 + 65*x^9 + 74*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 94*x^4 + 75*x^3 + 36*x^2 + 29*x + 74, x^95 + 15*x^93 + 110*x^92 + 5*x^91 + 44*x^90 + 99*x^89 + 10*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 110*x^84 + 121*x^83 + 116*x^82 + 63*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 99*x^75 + 68*x^74 + 21*x^73 + 118*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 2*x^68 + 71*x^67 + 92*x^66 + 33*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 121*x^27 + 28*x^26 + 15*x^25 + 50*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 102*x^20 + 29*x^19 + 4*x^18 + 123*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 7*x^11 + 52*x^10 + 17*x^9 + 62*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 26*x^4 + 59*x^3 + 108*x^2 + 13*x + 126, x^95 + 15*x^93 + 54*x^92 + 85*x^91 + 124*x^90 + 51*x^89 + 2*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 118*x^84 + 105*x^83 + 36*x^82 + 47*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 83*x^75 + 52*x^74 + 5*x^73 + 126*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 58*x^68 + 23*x^67 + 108*x^66 + 113*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 9*x^27 + 44*x^26 + 31*x^25 + 10*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 14*x^20 + 77*x^19 + 116*x^18 + 43*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 55*x^11 + 100*x^10 + 65*x^9 + 38*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 114*x^4 + 75*x^3 + 60*x^2 + 29*x + 38, x^95 + 15*x^93 + 106*x^92 + 53*x^91 + 36*x^90 + 19*x^89 + 62*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 106*x^84 + 9*x^83 + 60*x^82 + 79*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 115*x^75 + 44*x^74 + 37*x^73 + 66*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 102*x^68 + 119*x^67 + 52*x^66 + 81*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 105*x^27 + 116*x^26 + 127*x^25 + 54*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 82*x^20 + 109*x^19 + 108*x^18 + 75*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 87*x^11 + 124*x^10 + 97*x^9 + 26*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 46*x^4 + 43*x^3 + 100*x^2 + 125*x + 90, x^95 + 15*x^93 + 114*x^92 + 37*x^91 + 52*x^90 + 3*x^89 + 54*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 50*x^84 + 89*x^83 + 44*x^82 + 31*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 67*x^75 + 92*x^74 + 117*x^73 + 74*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 94*x^68 + 103*x^67 + 4*x^66 + 65*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 25*x^27 + 68*x^26 + 47*x^25 + 14*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 58*x^20 + 125*x^19 + 28*x^18 + 91*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 103*x^11 + 108*x^10 + 113*x^9 + 2*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 70*x^4 + 91*x^3 + 116*x^2 + 45*x + 2, x^95 + 15*x^93 + 78*x^92 + 117*x^91 + 92*x^90 + 51*x^89 + 58*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 46*x^84 + 73*x^83 + 4*x^82 + 47*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 51*x^75 + 84*x^74 + 5*x^73 + 6*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 2*x^68 + 55*x^67 + 12*x^66 + 113*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 41*x^27 + 12*x^26 + 31*x^25 + 34*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 38*x^20 + 45*x^19 + 84*x^18 + 43*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 23*x^11 + 4*x^10 + 65*x^9 + 14*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 26*x^4 + 107*x^3 + 92*x^2 + 29*x + 46, x^95 + 15*x^93 + 46*x^92 + 21*x^91 + 28*x^90 + 19*x^89 + 90*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 14*x^84 + 41*x^83 + 68*x^82 + 79*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 19*x^75 + 20*x^74 + 37*x^73 + 102*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 34*x^68 + 87*x^67 + 76*x^66 + 81*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 73*x^27 + 76*x^26 + 127*x^25 + 66*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 6*x^20 + 13*x^19 + 20*x^18 + 75*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 119*x^11 + 68*x^10 + 97*x^9 + 110*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 58*x^4 + 11*x^3 + 28*x^2 + 125*x + 14, x^95 + 15*x^93 + 2*x^92 + 69*x^91 + 84*x^90 + 35*x^89 + 38*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 66*x^84 + 57*x^83 + 12*x^82 + 127*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 35*x^75 + 60*x^74 + 85*x^73 + 90*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 78*x^68 + 7*x^67 + 36*x^66 + 97*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 57*x^27 + 100*x^26 + 79*x^25 + 62*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 10*x^20 + 93*x^19 + 124*x^18 + 59*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 71*x^11 + 76*x^10 + 81*x^9 + 82*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 118*x^4 + 123*x^3 + 20*x^2 + 77*x + 82, x^95 + 15*x^93 + 26*x^92 + 5*x^91 + 52*x^90 + 67*x^89 + 94*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 122*x^84 + 121*x^83 + 108*x^82 + 95*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 99*x^75 + 92*x^74 + 53*x^73 + 98*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 22*x^68 + 71*x^67 + 68*x^66 + x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 121*x^27 + 68*x^26 + 111*x^25 + 86*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 34*x^20 + 29*x^19 + 92*x^18 + 27*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 7*x^11 + 108*x^10 + 49*x^9 + 58*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 30*x^4 + 59*x^3 + 52*x^2 + 109*x + 90, x^95 + 15*x^93 + 46*x^92 + 37*x^91 + 12*x^90 + 3*x^89 + 42*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 110*x^84 + 89*x^83 + 20*x^82 + 31*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 67*x^75 + 100*x^74 + 117*x^73 + 86*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 2*x^68 + 103*x^67 + 60*x^66 + 65*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 25*x^27 + 124*x^26 + 47*x^25 + 82*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 102*x^20 + 125*x^19 + 36*x^18 + 91*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 103*x^11 + 84*x^10 + 113*x^9 + 30*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 26*x^4 + 91*x^3 + 76*x^2 + 45*x + 30, x^95 + 15*x^93 + 122*x^92 + 69*x^91 + 84*x^90 + 3*x^89 + 30*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 26*x^84 + 57*x^83 + 76*x^82 + 31*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 35*x^75 + 60*x^74 + 117*x^73 + 34*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 118*x^68 + 7*x^67 + 100*x^66 + 65*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 57*x^27 + 100*x^26 + 47*x^25 + 22*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 66*x^20 + 93*x^19 + 60*x^18 + 91*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 71*x^11 + 76*x^10 + 113*x^9 + 122*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 126*x^4 + 123*x^3 + 84*x^2 + 45*x + 90, x^95 + 15*x^93 + 22*x^92 + 5*x^91 + 12*x^90 + 67*x^89 + 82*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 118*x^84 + 121*x^83 + 84*x^82 + 95*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 99*x^75 + 100*x^74 + 53*x^73 + 110*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 122*x^68 + 71*x^67 + 124*x^66 + x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 121*x^27 + 124*x^26 + 111*x^25 + 26*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 14*x^20 + 29*x^19 + 100*x^18 + 27*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 7*x^11 + 84*x^10 + 49*x^9 + 86*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 50*x^4 + 59*x^3 + 12*x^2 + 109*x + 118, x^95 + 15*x^93 + 54*x^92 + 85*x^91 + 28*x^90 + 115*x^89 + 34*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 54*x^84 + 105*x^83 + 4*x^82 + 111*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 83*x^75 + 20*x^74 + 69*x^73 + 94*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 122*x^68 + 23*x^67 + 12*x^66 + 49*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 9*x^27 + 76*x^26 + 95*x^25 + 42*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 78*x^20 + 77*x^19 + 84*x^18 + 107*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 55*x^11 + 68*x^10 + x^9 + 6*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 50*x^4 + 75*x^3 + 92*x^2 + 93*x + 70, x^95 + 15*x^93 + 66*x^92 + 53*x^91 + 36*x^90 + 115*x^89 + 22*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 34*x^84 + 9*x^83 + 124*x^82 + 111*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 115*x^75 + 44*x^74 + 69*x^73 + 42*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 46*x^68 + 119*x^67 + 116*x^66 + 49*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 105*x^27 + 116*x^26 + 95*x^25 + 110*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 106*x^20 + 109*x^19 + 44*x^18 + 107*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 87*x^11 + 124*x^10 + x^9 + 98*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 86*x^4 + 43*x^3 + 36*x^2 + 93*x + 2, x^95 + 15*x^93 + 66*x^92 + 21*x^91 + 4*x^90 + 83*x^89 + 118*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 98*x^84 + 41*x^83 + 28*x^82 + 15*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 19*x^75 + 76*x^74 + 101*x^73 + 74*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 110*x^68 + 87*x^67 + 84*x^66 + 17*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 73*x^27 + 84*x^26 + 63*x^25 + 78*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 42*x^20 + 13*x^19 + 76*x^18 + 11*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 119*x^11 + 28*x^10 + 33*x^9 + 2*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 22*x^4 + 11*x^3 + 4*x^2 + 61*x + 98, x^95 + 15*x^93 + 62*x^92 + 117*x^91 + 92*x^90 + 51*x^89 + 106*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 94*x^84 + 73*x^83 + 4*x^82 + 47*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 51*x^75 + 84*x^74 + 5*x^73 + 86*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 82*x^68 + 55*x^67 + 12*x^66 + 113*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 41*x^27 + 12*x^26 + 31*x^25 + 18*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 22*x^20 + 45*x^19 + 84*x^18 + 43*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 23*x^11 + 4*x^10 + 65*x^9 + 30*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 42*x^4 + 107*x^3 + 92*x^2 + 29*x + 126, x^95 + 15*x^93 + 70*x^92 + 5*x^91 + 44*x^90 + 67*x^89 + 34*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 38*x^84 + 121*x^83 + 52*x^82 + 95*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 99*x^75 + 68*x^74 + 53*x^73 + 30*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 74*x^68 + 71*x^67 + 28*x^66 + x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 121*x^27 + 28*x^26 + 111*x^25 + 42*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 126*x^20 + 29*x^19 + 68*x^18 + 27*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 7*x^11 + 52*x^10 + 49*x^9 + 70*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 66*x^4 + 59*x^3 + 44*x^2 + 109*x + 102, x^95 + 15*x^93 + 22*x^92 + 69*x^91 + 12*x^90 + 3*x^89 + 82*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 118*x^84 + 57*x^83 + 84*x^82 + 31*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 35*x^75 + 100*x^74 + 117*x^73 + 110*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 122*x^68 + 7*x^67 + 124*x^66 + 65*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 57*x^27 + 124*x^26 + 47*x^25 + 26*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 14*x^20 + 93*x^19 + 100*x^18 + 91*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 71*x^11 + 84*x^10 + 113*x^9 + 86*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 50*x^4 + 123*x^3 + 12*x^2 + 45*x + 118, x^95 + 15*x^93 + 22*x^92 + 101*x^91 + 108*x^90 + 35*x^89 + 50*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 54*x^84 + 25*x^83 + 116*x^82 + 127*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 3*x^75 + 4*x^74 + 85*x^73 + 14*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 58*x^68 + 39*x^67 + 92*x^66 + 97*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 89*x^27 + 92*x^26 + 79*x^25 + 122*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 78*x^20 + 61*x^19 + 4*x^18 + 59*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 39*x^11 + 116*x^10 + 81*x^9 + 118*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 114*x^4 + 27*x^3 + 108*x^2 + 77*x + 86, x^95 + 15*x^93 + 6*x^92 + 53*x^91 + 124*x^90 + 83*x^89 + 18*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 6*x^84 + 9*x^83 + 36*x^82 + 15*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 115*x^75 + 52*x^74 + 101*x^73 + 110*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 42*x^68 + 119*x^67 + 108*x^66 + 17*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 105*x^27 + 44*x^26 + 63*x^25 + 90*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 94*x^20 + 109*x^19 + 116*x^18 + 11*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 87*x^11 + 100*x^10 + 33*x^9 + 86*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 34*x^4 + 43*x^3 + 60*x^2 + 61*x + 22, x^95 + 15*x^93 + 58*x^92 + 117*x^91 + 100*x^90 + 83*x^89 + 14*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 122*x^84 + 73*x^83 + 124*x^82 + 15*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 51*x^75 + 108*x^74 + 101*x^73 + 114*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 86*x^68 + 55*x^67 + 116*x^66 + 17*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 41*x^27 + 52*x^26 + 63*x^25 + 70*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 34*x^20 + 45*x^19 + 44*x^18 + 11*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 23*x^11 + 60*x^10 + 33*x^9 + 10*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 94*x^4 + 107*x^3 + 36*x^2 + 61*x + 10, x^95 + 15*x^93 + 46*x^92 + 101*x^91 + 12*x^90 + 67*x^89 + 42*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 110*x^84 + 25*x^83 + 20*x^82 + 95*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 3*x^75 + 100*x^74 + 53*x^73 + 86*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 2*x^68 + 39*x^67 + 60*x^66 + x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 89*x^27 + 124*x^26 + 111*x^25 + 82*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 102*x^20 + 61*x^19 + 36*x^18 + 27*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 39*x^11 + 84*x^10 + 49*x^9 + 30*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 26*x^4 + 27*x^3 + 76*x^2 + 109*x + 30, x^95 + 15*x^93 + 38*x^92 + 85*x^91 + 28*x^90 + 115*x^89 + 82*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 102*x^84 + 105*x^83 + 4*x^82 + 111*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 83*x^75 + 20*x^74 + 69*x^73 + 46*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 74*x^68 + 23*x^67 + 12*x^66 + 49*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 9*x^27 + 76*x^26 + 95*x^25 + 26*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 62*x^20 + 77*x^19 + 84*x^18 + 107*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 55*x^11 + 68*x^10 + x^9 + 22*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 66*x^4 + 75*x^3 + 92*x^2 + 93*x + 22, x^95 + 15*x^93 + 126*x^92 + 101*x^91 + 76*x^90 + 67*x^89 + 122*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 126*x^84 + 25*x^83 + 84*x^82 + 95*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 3*x^75 + 36*x^74 + 53*x^73 + 6*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 114*x^68 + 39*x^67 + 124*x^66 + x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 89*x^27 + 60*x^26 + 111*x^25 + 98*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 54*x^20 + 61*x^19 + 100*x^18 + 27*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 39*x^11 + 20*x^10 + 49*x^9 + 14*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 74*x^4 + 27*x^3 + 12*x^2 + 109*x + 78, x^95 + 15*x^93 + 94*x^92 + 37*x^91 + 12*x^90 + 3*x^89 + 26*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 94*x^84 + 89*x^83 + 20*x^82 + 31*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 67*x^75 + 100*x^74 + 117*x^73 + 102*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 18*x^68 + 103*x^67 + 60*x^66 + 65*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 25*x^27 + 124*x^26 + 47*x^25 + 2*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 22*x^20 + 125*x^19 + 36*x^18 + 91*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 103*x^11 + 84*x^10 + 113*x^9 + 110*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 106*x^4 + 91*x^3 + 76*x^2 + 45*x + 46, x^95 + 15*x^93 + 98*x^92 + 101*x^91 + 20*x^90 + 3*x^89 + 70*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 34*x^84 + 25*x^83 + 76*x^82 + 31*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 3*x^75 + 124*x^74 + 117*x^73 + 58*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 110*x^68 + 39*x^67 + 100*x^66 + 65*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 89*x^27 + 36*x^26 + 47*x^25 + 94*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 106*x^20 + 61*x^19 + 60*x^18 + 91*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 39*x^11 + 12*x^10 + 113*x^9 + 50*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 22*x^4 + 27*x^3 + 84*x^2 + 45*x + 50, x^95 + 15*x^93 + 126*x^92 + 5*x^91 + 44*x^90 + 99*x^89 + 90*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 62*x^84 + 121*x^83 + 116*x^82 + 63*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 99*x^75 + 68*x^74 + 21*x^73 + 38*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 50*x^68 + 71*x^67 + 92*x^66 + 33*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 121*x^27 + 28*x^26 + 15*x^25 + 66*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 118*x^20 + 29*x^19 + 4*x^18 + 123*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 7*x^11 + 52*x^10 + 17*x^9 + 46*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 10*x^4 + 59*x^3 + 108*x^2 + 13*x + 46, x^95 + 15*x^93 + 62*x^92 + 85*x^91 + 124*x^90 + 83*x^89 + 74*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 30*x^84 + 105*x^83 + 100*x^82 + 15*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 83*x^75 + 52*x^74 + 101*x^73 + 118*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 18*x^68 + 23*x^67 + 44*x^66 + 17*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 9*x^27 + 44*x^26 + 63*x^25 + 114*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 86*x^20 + 77*x^19 + 52*x^18 + 11*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 55*x^11 + 100*x^10 + 33*x^9 + 62*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 106*x^4 + 75*x^3 + 124*x^2 + 61*x + 94, x^95 + 15*x^93 + 110*x^92 + 37*x^91 + 12*x^90 + 3*x^89 + 106*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 46*x^84 + 89*x^83 + 20*x^82 + 31*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 67*x^75 + 100*x^74 + 117*x^73 + 22*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 66*x^68 + 103*x^67 + 60*x^66 + 65*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 25*x^27 + 124*x^26 + 47*x^25 + 18*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 38*x^20 + 125*x^19 + 36*x^18 + 91*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 103*x^11 + 84*x^10 + 113*x^9 + 94*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 90*x^4 + 91*x^3 + 76*x^2 + 45*x + 94, x^95 + 15*x^93 + 62*x^92 + 101*x^91 + 12*x^90 + 3*x^89 + 58*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 62*x^84 + 25*x^83 + 20*x^82 + 31*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 3*x^75 + 100*x^74 + 117*x^73 + 70*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 50*x^68 + 39*x^67 + 60*x^66 + 65*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 89*x^27 + 124*x^26 + 47*x^25 + 34*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 118*x^20 + 61*x^19 + 36*x^18 + 91*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 39*x^11 + 84*x^10 + 113*x^9 + 78*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 10*x^4 + 27*x^3 + 76*x^2 + 45*x + 14, x^95 + 15*x^93 + 98*x^92 + 85*x^91 + 100*x^90 + 83*x^89 + 118*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 66*x^84 + 105*x^83 + 60*x^82 + 15*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 83*x^75 + 108*x^74 + 101*x^73 + 74*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 14*x^68 + 23*x^67 + 52*x^66 + 17*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 9*x^27 + 52*x^26 + 63*x^25 + 78*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 10*x^20 + 77*x^19 + 108*x^18 + 11*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 55*x^11 + 60*x^10 + 33*x^9 + 2*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 54*x^4 + 75*x^3 + 100*x^2 + 61*x + 34, x^95 + 15*x^93 + 54*x^92 + 117*x^91 + 28*x^90 + 83*x^89 + 34*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 54*x^84 + 73*x^83 + 4*x^82 + 15*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 51*x^75 + 20*x^74 + 101*x^73 + 94*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 122*x^68 + 55*x^67 + 12*x^66 + 17*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 41*x^27 + 76*x^26 + 63*x^25 + 42*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 78*x^20 + 45*x^19 + 84*x^18 + 11*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 23*x^11 + 68*x^10 + 33*x^9 + 6*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 50*x^4 + 107*x^3 + 92*x^2 + 61*x + 70, x^95 + 15*x^93 + 46*x^92 + 53*x^91 + 124*x^90 + 51*x^89 + 58*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 78*x^84 + 9*x^83 + 100*x^82 + 47*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 115*x^75 + 52*x^74 + 5*x^73 + 6*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 98*x^68 + 119*x^67 + 44*x^66 + 113*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 105*x^27 + 44*x^26 + 31*x^25 + 34*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 70*x^20 + 109*x^19 + 52*x^18 + 43*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 87*x^11 + 100*x^10 + 65*x^9 + 14*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 122*x^4 + 43*x^3 + 124*x^2 + 29*x + 110, x^95 + 15*x^93 + 58*x^92 + 21*x^91 + 68*x^90 + 51*x^89 + 46*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 58*x^84 + 41*x^83 + 28*x^82 + 47*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 19*x^75 + 12*x^74 + 5*x^73 + 82*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 22*x^68 + 87*x^67 + 84*x^66 + 113*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 73*x^27 + 20*x^26 + 31*x^25 + 102*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 98*x^20 + 13*x^19 + 76*x^18 + 43*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 119*x^11 + 92*x^10 + 65*x^9 + 106*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 30*x^4 + 11*x^3 + 4*x^2 + 29*x + 42, x^95 + 15*x^93 + 58*x^92 + 37*x^91 + 116*x^90 + 35*x^89 + 62*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 26*x^84 + 89*x^83 + 44*x^82 + 127*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 67*x^75 + 28*x^74 + 85*x^73 + 2*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 118*x^68 + 103*x^67 + 4*x^66 + 97*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 25*x^27 + 4*x^26 + 79*x^25 + 54*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 66*x^20 + 125*x^19 + 28*x^18 + 59*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 103*x^11 + 44*x^10 + 81*x^9 + 90*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 126*x^4 + 91*x^3 + 116*x^2 + 77*x + 122, x^95 + 15*x^93 + 98*x^92 + 69*x^91 + 116*x^90 + 99*x^89 + 38*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 98*x^84 + 57*x^83 + 108*x^82 + 63*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 35*x^75 + 28*x^74 + 21*x^73 + 90*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 46*x^68 + 7*x^67 + 68*x^66 + 33*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 57*x^27 + 4*x^26 + 15*x^25 + 62*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 42*x^20 + 93*x^19 + 92*x^18 + 123*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 71*x^11 + 44*x^10 + 17*x^9 + 82*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 86*x^4 + 123*x^3 + 52*x^2 + 13*x + 18, x^95 + 15*x^93 + 102*x^92 + 53*x^91 + 60*x^90 + 83*x^89 + 50*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 102*x^84 + 9*x^83 + 100*x^82 + 15*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 115*x^75 + 116*x^74 + 101*x^73 + 78*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 74*x^68 + 119*x^67 + 44*x^66 + 17*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 105*x^27 + 108*x^26 + 63*x^25 + 122*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 62*x^20 + 109*x^19 + 52*x^18 + 11*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 87*x^11 + 36*x^10 + 33*x^9 + 54*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 66*x^4 + 43*x^3 + 124*x^2 + 61*x + 118, x^95 + 15*x^93 + 74*x^92 + 85*x^91 + 68*x^90 + 115*x^89 + 126*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 10*x^84 + 105*x^83 + 28*x^82 + 111*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 83*x^75 + 12*x^74 + 69*x^73 + 2*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 70*x^68 + 23*x^67 + 84*x^66 + 49*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 9*x^27 + 20*x^26 + 95*x^25 + 118*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 114*x^20 + 77*x^19 + 76*x^18 + 107*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 55*x^11 + 92*x^10 + x^9 + 90*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 14*x^4 + 75*x^3 + 4*x^2 + 93*x + 90, x^95 + 15*x^93 + 54*x^92 + 69*x^91 + 12*x^90 + 3*x^89 + 114*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 22*x^84 + 57*x^83 + 84*x^82 + 31*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 35*x^75 + 100*x^74 + 117*x^73 + 78*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 90*x^68 + 7*x^67 + 124*x^66 + 65*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 57*x^27 + 124*x^26 + 47*x^25 + 58*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 46*x^20 + 93*x^19 + 100*x^18 + 91*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 71*x^11 + 84*x^10 + 113*x^9 + 54*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 18*x^4 + 123*x^3 + 12*x^2 + 45*x + 86, x^95 + 15*x^93 + 74*x^92 + 5*x^91 + 20*x^90 + 3*x^89 + 46*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 42*x^84 + 121*x^83 + 12*x^82 + 31*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 99*x^75 + 124*x^74 + 117*x^73 + 18*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 102*x^68 + 71*x^67 + 36*x^66 + 65*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 121*x^27 + 36*x^26 + 47*x^25 + 102*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 18*x^20 + 29*x^19 + 124*x^18 + 91*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 7*x^11 + 12*x^10 + 113*x^9 + 42*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 46*x^4 + 59*x^3 + 20*x^2 + 45*x + 74, x^95 + 15*x^93 + 78*x^92 + 69*x^91 + 108*x^90 + 99*x^89 + 106*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 78*x^84 + 57*x^83 + 52*x^82 + 63*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 35*x^75 + 4*x^74 + 21*x^73 + 22*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 34*x^68 + 7*x^67 + 28*x^66 + 33*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 57*x^27 + 92*x^26 + 15*x^25 + 18*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 70*x^20 + 93*x^19 + 68*x^18 + 123*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 71*x^11 + 116*x^10 + 17*x^9 + 94*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 58*x^4 + 123*x^3 + 44*x^2 + 13*x + 30, x^95 + 15*x^93 + 26*x^92 + 85*x^91 + 68*x^90 + 115*x^89 + 14*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 26*x^84 + 105*x^83 + 28*x^82 + 111*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 83*x^75 + 12*x^74 + 69*x^73 + 114*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 54*x^68 + 23*x^67 + 84*x^66 + 49*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 9*x^27 + 20*x^26 + 95*x^25 + 70*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 66*x^20 + 77*x^19 + 76*x^18 + 107*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 55*x^11 + 92*x^10 + x^9 + 10*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 62*x^4 + 75*x^3 + 4*x^2 + 93*x + 74, x^95 + 15*x^93 + 42*x^92 + 21*x^91 + 36*x^90 + 51*x^89 + 126*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 42*x^84 + 41*x^83 + 60*x^82 + 47*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 19*x^75 + 44*x^74 + 5*x^73 + 2*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 38*x^68 + 87*x^67 + 52*x^66 + 113*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 73*x^27 + 116*x^26 + 31*x^25 + 118*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 18*x^20 + 13*x^19 + 108*x^18 + 43*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 119*x^11 + 124*x^10 + 65*x^9 + 90*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 110*x^4 + 11*x^3 + 100*x^2 + 29*x + 26, x^95 + 15*x^93 + 6*x^92 + 117*x^91 + 28*x^90 + 19*x^89 + 114*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 70*x^84 + 73*x^83 + 4*x^82 + 79*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 51*x^75 + 20*x^74 + 37*x^73 + 14*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 106*x^68 + 55*x^67 + 12*x^66 + 81*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 41*x^27 + 76*x^26 + 127*x^25 + 58*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 30*x^20 + 45*x^19 + 84*x^18 + 75*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 23*x^11 + 68*x^10 + 97*x^9 + 118*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 98*x^4 + 107*x^3 + 92*x^2 + 125*x + 118, x^95 + 15*x^93 + 118*x^92 + 53*x^91 + 28*x^90 + 83*x^89 + 34*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 118*x^84 + 9*x^83 + 4*x^82 + 15*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 115*x^75 + 20*x^74 + 101*x^73 + 94*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 58*x^68 + 119*x^67 + 12*x^66 + 17*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 105*x^27 + 76*x^26 + 63*x^25 + 42*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 14*x^20 + 109*x^19 + 84*x^18 + 11*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 87*x^11 + 68*x^10 + 33*x^9 + 6*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 114*x^4 + 43*x^3 + 92*x^2 + 61*x + 70, x^95 + 15*x^93 + 18*x^92 + 53*x^91 + 100*x^90 + 51*x^89 + 38*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 50*x^84 + 9*x^83 + 60*x^82 + 47*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 115*x^75 + 108*x^74 + 5*x^73 + 26*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 30*x^68 + 119*x^67 + 52*x^66 + 113*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 105*x^27 + 52*x^26 + 31*x^25 + 62*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 58*x^20 + 109*x^19 + 108*x^18 + 43*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 87*x^11 + 60*x^10 + 65*x^9 + 18*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 6*x^4 + 43*x^3 + 100*x^2 + 29*x + 114, x^95 + 15*x^93 + 126*x^92 + 85*x^91 + 60*x^90 + 19*x^89 + 10*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 94*x^84 + 105*x^83 + 36*x^82 + 79*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 83*x^75 + 116*x^74 + 37*x^73 + 54*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 82*x^68 + 23*x^67 + 108*x^66 + 81*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 9*x^27 + 108*x^26 + 127*x^25 + 50*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 22*x^20 + 77*x^19 + 116*x^18 + 75*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 55*x^11 + 36*x^10 + 97*x^9 + 126*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 42*x^4 + 75*x^3 + 60*x^2 + 125*x + 30, x^95 + 15*x^93 + 78*x^92 + 5*x^91 + 108*x^90 + 99*x^89 + 42*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 78*x^84 + 121*x^83 + 52*x^82 + 63*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 99*x^75 + 4*x^74 + 21*x^73 + 86*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 34*x^68 + 71*x^67 + 28*x^66 + 33*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 121*x^27 + 92*x^26 + 15*x^25 + 82*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 70*x^20 + 29*x^19 + 68*x^18 + 123*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 7*x^11 + 116*x^10 + 17*x^9 + 30*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 58*x^4 + 59*x^3 + 44*x^2 + 13*x + 94, x^95 + 15*x^93 + 94*x^92 + 5*x^91 + 12*x^90 + 99*x^89 + 90*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 94*x^84 + 121*x^83 + 20*x^82 + 63*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 99*x^75 + 100*x^74 + 21*x^73 + 38*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 18*x^68 + 71*x^67 + 60*x^66 + 33*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 121*x^27 + 124*x^26 + 15*x^25 + 66*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 22*x^20 + 29*x^19 + 36*x^18 + 123*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 7*x^11 + 84*x^10 + 17*x^9 + 46*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 106*x^4 + 59*x^3 + 76*x^2 + 13*x + 110, x^95 + 15*x^93 + 42*x^92 + 37*x^91 + 84*x^90 + 99*x^89 + 78*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 10*x^84 + 89*x^83 + 76*x^82 + 63*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 67*x^75 + 60*x^74 + 21*x^73 + 114*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 6*x^68 + 103*x^67 + 100*x^66 + 33*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 25*x^27 + 100*x^26 + 15*x^25 + 6*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 114*x^20 + 125*x^19 + 60*x^18 + 123*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 103*x^11 + 76*x^10 + 17*x^9 + 10*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 78*x^4 + 91*x^3 + 84*x^2 + 13*x + 42, x^95 + 15*x^93 + 74*x^92 + 69*x^91 + 20*x^90 + 67*x^89 + 46*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 42*x^84 + 57*x^83 + 12*x^82 + 95*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 35*x^75 + 124*x^74 + 53*x^73 + 18*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 102*x^68 + 7*x^67 + 36*x^66 + x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 57*x^27 + 36*x^26 + 111*x^25 + 102*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 18*x^20 + 93*x^19 + 124*x^18 + 27*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 71*x^11 + 12*x^10 + 49*x^9 + 42*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 46*x^4 + 123*x^3 + 20*x^2 + 109*x + 74, x^95 + 15*x^93 + 26*x^92 + 101*x^91 + 116*x^90 + 99*x^89 + 30*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 122*x^84 + 25*x^83 + 44*x^82 + 63*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 3*x^75 + 28*x^74 + 21*x^73 + 34*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 22*x^68 + 39*x^67 + 4*x^66 + 33*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 89*x^27 + 4*x^26 + 15*x^25 + 22*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 34*x^20 + 61*x^19 + 28*x^18 + 123*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 39*x^11 + 44*x^10 + 17*x^9 + 122*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 30*x^4 + 27*x^3 + 116*x^2 + 13*x + 26, x^95 + 15*x^93 + 106*x^92 + 117*x^91 + 4*x^90 + 19*x^89 + 30*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 42*x^84 + 73*x^83 + 92*x^82 + 79*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 51*x^75 + 76*x^74 + 37*x^73 + 98*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 38*x^68 + 55*x^67 + 20*x^66 + 81*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 41*x^27 + 84*x^26 + 127*x^25 + 22*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 18*x^20 + 45*x^19 + 12*x^18 + 75*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 23*x^11 + 28*x^10 + 97*x^9 + 58*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 110*x^4 + 107*x^3 + 68*x^2 + 125*x + 58, x^95 + 15*x^93 + 118*x^92 + 37*x^91 + 108*x^90 + 99*x^89 + 18*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 22*x^84 + 89*x^83 + 116*x^82 + 63*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 67*x^75 + 4*x^74 + 21*x^73 + 46*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 90*x^68 + 103*x^67 + 92*x^66 + 33*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 25*x^27 + 92*x^26 + 15*x^25 + 90*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 46*x^20 + 125*x^19 + 4*x^18 + 123*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 103*x^11 + 116*x^10 + 17*x^9 + 22*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 18*x^4 + 91*x^3 + 108*x^2 + 13*x + 118, x^95 + 15*x^93 + 30*x^92 + 5*x^91 + 12*x^90 + 99*x^89 + 26*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 30*x^84 + 121*x^83 + 20*x^82 + 63*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 99*x^75 + 100*x^74 + 21*x^73 + 102*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 82*x^68 + 71*x^67 + 60*x^66 + 33*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 121*x^27 + 124*x^26 + 15*x^25 + 2*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 86*x^20 + 29*x^19 + 36*x^18 + 123*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 7*x^11 + 84*x^10 + 17*x^9 + 110*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 42*x^4 + 59*x^3 + 76*x^2 + 13*x + 46, x^95 + 15*x^93 + 90*x^92 + 69*x^91 + 84*x^90 + 3*x^89 + 126*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 122*x^84 + 57*x^83 + 76*x^82 + 31*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 35*x^75 + 60*x^74 + 117*x^73 + 66*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 22*x^68 + 7*x^67 + 100*x^66 + 65*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 57*x^27 + 100*x^26 + 47*x^25 + 118*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 34*x^20 + 93*x^19 + 60*x^18 + 91*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 71*x^11 + 76*x^10 + 113*x^9 + 26*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 30*x^4 + 123*x^3 + 84*x^2 + 45*x + 122, x^95 + 15*x^93 + 50*x^92 + 37*x^91 + 52*x^90 + 3*x^89 + 118*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 114*x^84 + 89*x^83 + 44*x^82 + 31*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 67*x^75 + 92*x^74 + 117*x^73 + 10*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 30*x^68 + 103*x^67 + 4*x^66 + 65*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 25*x^27 + 68*x^26 + 47*x^25 + 78*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 122*x^20 + 125*x^19 + 28*x^18 + 91*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 103*x^11 + 108*x^10 + 113*x^9 + 66*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 6*x^4 + 91*x^3 + 116*x^2 + 45*x + 66, x^95 + 15*x^93 + 34*x^92 + 21*x^91 + 36*x^90 + 83*x^89 + 54*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 2*x^84 + 41*x^83 + 124*x^82 + 15*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 19*x^75 + 44*x^74 + 101*x^73 + 10*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 78*x^68 + 87*x^67 + 116*x^66 + 17*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 73*x^27 + 116*x^26 + 63*x^25 + 14*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 74*x^20 + 13*x^19 + 44*x^18 + 11*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 119*x^11 + 124*x^10 + 33*x^9 + 66*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 118*x^4 + 11*x^3 + 36*x^2 + 61*x + 98, x^95 + 15*x^93 + 78*x^92 + 85*x^91 + 92*x^90 + 19*x^89 + 122*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 46*x^84 + 105*x^83 + 4*x^82 + 79*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 83*x^75 + 84*x^74 + 37*x^73 + 70*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 2*x^68 + 23*x^67 + 12*x^66 + 81*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 9*x^27 + 12*x^26 + 127*x^25 + 98*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 38*x^20 + 77*x^19 + 84*x^18 + 75*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 55*x^11 + 4*x^10 + 97*x^9 + 78*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 26*x^4 + 75*x^3 + 92*x^2 + 125*x + 110, x^95 + 15*x^93 + 94*x^92 + 117*x^91 + 60*x^90 + 51*x^89 + 42*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 62*x^84 + 73*x^83 + 36*x^82 + 47*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 51*x^75 + 116*x^74 + 5*x^73 + 22*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 114*x^68 + 55*x^67 + 108*x^66 + 113*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 41*x^27 + 108*x^26 + 31*x^25 + 82*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 118*x^20 + 45*x^19 + 116*x^18 + 43*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 23*x^11 + 36*x^10 + 65*x^9 + 94*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 74*x^4 + 107*x^3 + 60*x^2 + 29*x + 126, x^95 + 15*x^93 + 90*x^92 + 117*x^91 + 36*x^90 + 83*x^89 + 110*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 26*x^84 + 73*x^83 + 60*x^82 + 15*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 51*x^75 + 44*x^74 + 101*x^73 + 18*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 54*x^68 + 55*x^67 + 52*x^66 + 17*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 41*x^27 + 116*x^26 + 63*x^25 + 38*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 66*x^20 + 45*x^19 + 108*x^18 + 11*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 23*x^11 + 124*x^10 + 33*x^9 + 42*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 62*x^4 + 107*x^3 + 100*x^2 + 61*x + 42, x^95 + 15*x^93 + 46*x^92 + 101*x^91 + 76*x^90 + 3*x^89 + 42*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 110*x^84 + 25*x^83 + 84*x^82 + 31*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 3*x^75 + 36*x^74 + 117*x^73 + 86*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 2*x^68 + 39*x^67 + 124*x^66 + 65*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 89*x^27 + 60*x^26 + 47*x^25 + 82*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 102*x^20 + 61*x^19 + 100*x^18 + 91*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 39*x^11 + 20*x^10 + 113*x^9 + 30*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 26*x^4 + 27*x^3 + 12*x^2 + 45*x + 30, x^95 + 15*x^93 + 82*x^92 + 5*x^91 + 116*x^90 + 35*x^89 + 86*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 18*x^84 + 121*x^83 + 108*x^82 + 127*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 99*x^75 + 28*x^74 + 85*x^73 + 42*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 126*x^68 + 71*x^67 + 68*x^66 + 97*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 121*x^27 + 4*x^26 + 79*x^25 + 46*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 26*x^20 + 29*x^19 + 92*x^18 + 59*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 7*x^11 + 44*x^10 + 81*x^9 + 98*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 102*x^4 + 59*x^3 + 52*x^2 + 77*x + 98, x^95 + 15*x^93 + 50*x^92 + 85*x^91 + 4*x^90 + 83*x^89 + 102*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 18*x^84 + 105*x^83 + 28*x^82 + 15*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 83*x^75 + 76*x^74 + 101*x^73 + 90*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 62*x^68 + 23*x^67 + 84*x^66 + 17*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 9*x^27 + 84*x^26 + 63*x^25 + 126*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 26*x^20 + 77*x^19 + 76*x^18 + 11*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 55*x^11 + 28*x^10 + 33*x^9 + 82*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 38*x^4 + 75*x^3 + 4*x^2 + 61*x + 114, x^95 + 15*x^93 + 30*x^92 + 53*x^91 + 60*x^90 + 115*x^89 + 106*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 126*x^84 + 9*x^83 + 36*x^82 + 111*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 115*x^75 + 116*x^74 + 69*x^73 + 86*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 50*x^68 + 119*x^67 + 108*x^66 + 49*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 105*x^27 + 108*x^26 + 95*x^25 + 18*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 54*x^20 + 109*x^19 + 116*x^18 + 107*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 87*x^11 + 36*x^10 + x^9 + 30*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 10*x^4 + 43*x^3 + 60*x^2 + 93*x + 62, x^95 + 15*x^93 + 10*x^92 + 69*x^91 + 20*x^90 + 3*x^89 + 46*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 106*x^84 + 57*x^83 + 12*x^82 + 31*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 35*x^75 + 124*x^74 + 117*x^73 + 18*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 38*x^68 + 7*x^67 + 36*x^66 + 65*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 57*x^27 + 36*x^26 + 47*x^25 + 102*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 82*x^20 + 93*x^19 + 124*x^18 + 91*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 71*x^11 + 12*x^10 + 113*x^9 + 42*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 110*x^4 + 123*x^3 + 20*x^2 + 45*x + 74, x^95 + 15*x^93 + 106*x^92 + 85*x^91 + 68*x^90 + 115*x^89 + 30*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 42*x^84 + 105*x^83 + 28*x^82 + 111*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 83*x^75 + 12*x^74 + 69*x^73 + 98*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 38*x^68 + 23*x^67 + 84*x^66 + 49*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 9*x^27 + 20*x^26 + 95*x^25 + 22*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 18*x^20 + 77*x^19 + 76*x^18 + 107*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 55*x^11 + 92*x^10 + x^9 + 58*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 110*x^4 + 75*x^3 + 4*x^2 + 93*x + 58, x^95 + 15*x^93 + 114*x^92 + 69*x^91 + 20*x^90 + 99*x^89 + 86*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 114*x^84 + 57*x^83 + 76*x^82 + 63*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 35*x^75 + 124*x^74 + 21*x^73 + 42*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 30*x^68 + 7*x^67 + 100*x^66 + 33*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 57*x^27 + 36*x^26 + 15*x^25 + 46*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 122*x^20 + 93*x^19 + 60*x^18 + 123*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 71*x^11 + 12*x^10 + 17*x^9 + 98*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 6*x^4 + 123*x^3 + 84*x^2 + 13*x + 34, x^95 + 15*x^93 + 38*x^92 + 85*x^91 + 92*x^90 + 115*x^89 + 18*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 102*x^84 + 105*x^83 + 68*x^82 + 111*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 83*x^75 + 84*x^74 + 69*x^73 + 110*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 74*x^68 + 23*x^67 + 76*x^66 + 49*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 9*x^27 + 12*x^26 + 95*x^25 + 90*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 62*x^20 + 77*x^19 + 20*x^18 + 107*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 55*x^11 + 4*x^10 + x^9 + 86*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 66*x^4 + 75*x^3 + 28*x^2 + 93*x + 86, x^95 + 15*x^93 + 98*x^92 + 21*x^91 + 36*x^90 + 19*x^89 + 54*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 66*x^84 + 41*x^83 + 124*x^82 + 79*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 19*x^75 + 44*x^74 + 37*x^73 + 10*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 14*x^68 + 87*x^67 + 116*x^66 + 81*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 73*x^27 + 116*x^26 + 127*x^25 + 14*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 10*x^20 + 13*x^19 + 44*x^18 + 75*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 119*x^11 + 124*x^10 + 97*x^9 + 66*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 54*x^4 + 11*x^3 + 36*x^2 + 125*x + 98, x^95 + 15*x^93 + 14*x^92 + 21*x^91 + 92*x^90 + 83*x^89 + 58*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 110*x^84 + 41*x^83 + 4*x^82 + 15*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 19*x^75 + 84*x^74 + 101*x^73 + 6*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 66*x^68 + 87*x^67 + 12*x^66 + 17*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 73*x^27 + 12*x^26 + 63*x^25 + 34*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 102*x^20 + 13*x^19 + 84*x^18 + 11*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 119*x^11 + 4*x^10 + 33*x^9 + 14*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 90*x^4 + 11*x^3 + 92*x^2 + 61*x + 46, x^95 + 15*x^93 + 118*x^92 + 85*x^91 + 92*x^90 + 115*x^89 + 34*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 118*x^84 + 105*x^83 + 68*x^82 + 111*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 83*x^75 + 84*x^74 + 69*x^73 + 94*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 58*x^68 + 23*x^67 + 76*x^66 + 49*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 9*x^27 + 12*x^26 + 95*x^25 + 42*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 14*x^20 + 77*x^19 + 20*x^18 + 107*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 55*x^11 + 4*x^10 + x^9 + 6*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 114*x^4 + 75*x^3 + 28*x^2 + 93*x + 70, x^95 + 15*x^93 + 98*x^92 + 5*x^91 + 84*x^90 + 99*x^89 + 6*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 34*x^84 + 121*x^83 + 12*x^82 + 63*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 99*x^75 + 60*x^74 + 21*x^73 + 122*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 110*x^68 + 71*x^67 + 36*x^66 + 33*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 121*x^27 + 100*x^26 + 15*x^25 + 30*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 106*x^20 + 29*x^19 + 124*x^18 + 123*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 7*x^11 + 76*x^10 + 17*x^9 + 114*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 22*x^4 + 59*x^3 + 20*x^2 + 13*x + 114, x^95 + 15*x^93 + 66*x^92 + 101*x^91 + 20*x^90 + 3*x^89 + 38*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 2*x^84 + 25*x^83 + 76*x^82 + 31*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 3*x^75 + 124*x^74 + 117*x^73 + 90*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 14*x^68 + 39*x^67 + 100*x^66 + 65*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 89*x^27 + 36*x^26 + 47*x^25 + 62*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 74*x^20 + 61*x^19 + 60*x^18 + 91*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 39*x^11 + 12*x^10 + 113*x^9 + 82*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 54*x^4 + 27*x^3 + 84*x^2 + 45*x + 82, x^95 + 15*x^93 + 46*x^92 + 53*x^91 + 92*x^90 + 51*x^89 + 90*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 14*x^84 + 9*x^83 + 4*x^82 + 47*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 115*x^75 + 84*x^74 + 5*x^73 + 102*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 34*x^68 + 119*x^67 + 12*x^66 + 113*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 105*x^27 + 12*x^26 + 31*x^25 + 66*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 6*x^20 + 109*x^19 + 84*x^18 + 43*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 87*x^11 + 4*x^10 + 65*x^9 + 110*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 58*x^4 + 43*x^3 + 92*x^2 + 29*x + 14, x^95 + 15*x^93 + 110*x^92 + 101*x^91 + 76*x^90 + 3*x^89 + 106*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 46*x^84 + 25*x^83 + 84*x^82 + 31*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 3*x^75 + 36*x^74 + 117*x^73 + 22*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 66*x^68 + 39*x^67 + 124*x^66 + 65*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 89*x^27 + 60*x^26 + 47*x^25 + 18*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 38*x^20 + 61*x^19 + 100*x^18 + 91*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 39*x^11 + 20*x^10 + 113*x^9 + 94*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 90*x^4 + 27*x^3 + 12*x^2 + 45*x + 94, x^95 + 15*x^93 + 42*x^92 + 5*x^91 + 84*x^90 + 3*x^89 + 78*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 10*x^84 + 121*x^83 + 76*x^82 + 31*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 99*x^75 + 60*x^74 + 117*x^73 + 114*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 6*x^68 + 71*x^67 + 100*x^66 + 65*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 121*x^27 + 100*x^26 + 47*x^25 + 6*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 114*x^20 + 29*x^19 + 60*x^18 + 91*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 7*x^11 + 76*x^10 + 113*x^9 + 10*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 78*x^4 + 59*x^3 + 84*x^2 + 45*x + 42, x^95 + 15*x^93 + 94*x^92 + 21*x^91 + 92*x^90 + 83*x^89 + 74*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 126*x^84 + 41*x^83 + 4*x^82 + 15*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 19*x^75 + 84*x^74 + 101*x^73 + 118*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 50*x^68 + 87*x^67 + 12*x^66 + 17*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 73*x^27 + 12*x^26 + 63*x^25 + 114*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 54*x^20 + 13*x^19 + 84*x^18 + 11*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 119*x^11 + 4*x^10 + 33*x^9 + 62*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 10*x^4 + 11*x^3 + 92*x^2 + 61*x + 30, x^95 + 15*x^93 + 58*x^92 + 69*x^91 + 20*x^90 + 67*x^89 + 94*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 90*x^84 + 57*x^83 + 12*x^82 + 95*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 35*x^75 + 124*x^74 + 53*x^73 + 98*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 54*x^68 + 7*x^67 + 36*x^66 + x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 57*x^27 + 36*x^26 + 111*x^25 + 86*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 2*x^20 + 93*x^19 + 124*x^18 + 27*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 71*x^11 + 12*x^10 + 49*x^9 + 58*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 62*x^4 + 123*x^3 + 20*x^2 + 109*x + 26, x^95 + 15*x^93 + 82*x^92 + 85*x^91 + 4*x^90 + 83*x^89 + 6*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 50*x^84 + 105*x^83 + 28*x^82 + 15*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 83*x^75 + 76*x^74 + 101*x^73 + 58*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 30*x^68 + 23*x^67 + 84*x^66 + 17*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 9*x^27 + 84*x^26 + 63*x^25 + 30*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 58*x^20 + 77*x^19 + 76*x^18 + 11*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 55*x^11 + 28*x^10 + 33*x^9 + 50*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 6*x^4 + 75*x^3 + 4*x^2 + 61*x + 82, x^95 + 15*x^93 + 58*x^92 + 53*x^91 + 4*x^90 + 19*x^89 + 110*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 58*x^84 + 9*x^83 + 92*x^82 + 79*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 115*x^75 + 76*x^74 + 37*x^73 + 18*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 22*x^68 + 119*x^67 + 20*x^66 + 81*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 105*x^27 + 84*x^26 + 127*x^25 + 38*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 98*x^20 + 109*x^19 + 12*x^18 + 75*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 87*x^11 + 28*x^10 + 97*x^9 + 42*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 30*x^4 + 43*x^3 + 68*x^2 + 125*x + 106, x^95 + 15*x^93 + 26*x^92 + 85*x^91 + 68*x^90 + 51*x^89 + 78*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 26*x^84 + 105*x^83 + 28*x^82 + 47*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 83*x^75 + 12*x^74 + 5*x^73 + 50*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 54*x^68 + 23*x^67 + 84*x^66 + 113*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 9*x^27 + 20*x^26 + 31*x^25 + 6*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 66*x^20 + 77*x^19 + 76*x^18 + 43*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 55*x^11 + 92*x^10 + 65*x^9 + 74*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 62*x^4 + 75*x^3 + 4*x^2 + 29*x + 10, x^95 + 15*x^93 + 66*x^92 + 37*x^91 + 84*x^90 + 67*x^89 + 102*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 2*x^84 + 89*x^83 + 12*x^82 + 95*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 67*x^75 + 60*x^74 + 53*x^73 + 26*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 14*x^68 + 103*x^67 + 36*x^66 + x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 25*x^27 + 100*x^26 + 111*x^25 + 126*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 74*x^20 + 125*x^19 + 124*x^18 + 27*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 103*x^11 + 76*x^10 + 49*x^9 + 18*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 54*x^4 + 91*x^3 + 20*x^2 + 109*x + 18, x^95 + 15*x^93 + 106*x^92 + 117*x^91 + 68*x^90 + 19*x^89 + 94*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 42*x^84 + 73*x^83 + 28*x^82 + 79*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 51*x^75 + 12*x^74 + 37*x^73 + 34*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 38*x^68 + 55*x^67 + 84*x^66 + 81*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 41*x^27 + 20*x^26 + 127*x^25 + 86*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 18*x^20 + 45*x^19 + 76*x^18 + 75*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 23*x^11 + 92*x^10 + 97*x^9 + 122*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 110*x^4 + 107*x^3 + 4*x^2 + 125*x + 122, x^95 + 15*x^93 + 110*x^92 + 53*x^91 + 92*x^90 + 51*x^89 + 26*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 78*x^84 + 9*x^83 + 4*x^82 + 47*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 115*x^75 + 84*x^74 + 5*x^73 + 38*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 98*x^68 + 119*x^67 + 12*x^66 + 113*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 105*x^27 + 12*x^26 + 31*x^25 + 2*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 70*x^20 + 109*x^19 + 84*x^18 + 43*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 87*x^11 + 4*x^10 + 65*x^9 + 46*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 122*x^4 + 43*x^3 + 92*x^2 + 29*x + 78, x^95 + 15*x^93 + 74*x^92 + 85*x^91 + 4*x^90 + 115*x^89 + 62*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 10*x^84 + 105*x^83 + 92*x^82 + 111*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 83*x^75 + 76*x^74 + 69*x^73 + 66*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 70*x^68 + 23*x^67 + 20*x^66 + 49*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 9*x^27 + 84*x^26 + 95*x^25 + 54*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 114*x^20 + 77*x^19 + 12*x^18 + 107*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 55*x^11 + 28*x^10 + x^9 + 26*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 14*x^4 + 75*x^3 + 68*x^2 + 93*x + 26, x^95 + 15*x^93 + 118*x^92 + 21*x^91 + 60*x^90 + 51*x^89 + 66*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 54*x^84 + 41*x^83 + 100*x^82 + 47*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 19*x^75 + 116*x^74 + 5*x^73 + 62*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 122*x^68 + 87*x^67 + 44*x^66 + 113*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 73*x^27 + 108*x^26 + 31*x^25 + 74*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 78*x^20 + 13*x^19 + 52*x^18 + 43*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 119*x^11 + 36*x^10 + 65*x^9 + 102*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 50*x^4 + 11*x^3 + 124*x^2 + 29*x + 102, x^95 + 15*x^93 + 70*x^92 + 5*x^91 + 108*x^90 + 3*x^89 + 34*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 38*x^84 + 121*x^83 + 116*x^82 + 31*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 99*x^75 + 4*x^74 + 117*x^73 + 30*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 74*x^68 + 71*x^67 + 92*x^66 + 65*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 121*x^27 + 92*x^26 + 47*x^25 + 42*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 126*x^20 + 29*x^19 + 4*x^18 + 91*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 7*x^11 + 116*x^10 + 113*x^9 + 70*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 66*x^4 + 59*x^3 + 108*x^2 + 45*x + 102, x^95 + 15*x^93 + 18*x^92 + 85*x^91 + 68*x^90 + 19*x^89 + 70*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 114*x^84 + 105*x^83 + 92*x^82 + 79*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 83*x^75 + 12*x^74 + 37*x^73 + 122*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 94*x^68 + 23*x^67 + 20*x^66 + 81*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 9*x^27 + 20*x^26 + 127*x^25 + 94*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 122*x^20 + 77*x^19 + 12*x^18 + 75*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 55*x^11 + 92*x^10 + 97*x^9 + 114*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 70*x^4 + 75*x^3 + 68*x^2 + 125*x + 18, x^95 + 15*x^93 + 126*x^92 + 37*x^91 + 12*x^90 + 3*x^89 + 58*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 126*x^84 + 89*x^83 + 20*x^82 + 31*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 67*x^75 + 100*x^74 + 117*x^73 + 70*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 114*x^68 + 103*x^67 + 60*x^66 + 65*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 25*x^27 + 124*x^26 + 47*x^25 + 34*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 54*x^20 + 125*x^19 + 36*x^18 + 91*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 103*x^11 + 84*x^10 + 113*x^9 + 78*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 74*x^4 + 91*x^3 + 76*x^2 + 45*x + 14, x^95 + 15*x^93 + 38*x^92 + 101*x^91 + 76*x^90 + 99*x^89 + 98*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 70*x^84 + 25*x^83 + 20*x^82 + 63*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 3*x^75 + 36*x^74 + 21*x^73 + 94*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 42*x^68 + 39*x^67 + 60*x^66 + 33*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 89*x^27 + 60*x^26 + 15*x^25 + 106*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 30*x^20 + 61*x^19 + 36*x^18 + 123*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 39*x^11 + 20*x^10 + 17*x^9 + 6*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 34*x^4 + 27*x^3 + 76*x^2 + 13*x + 102, x^95 + 15*x^93 + 110*x^92 + 21*x^91 + 124*x^90 + 19*x^89 + 58*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 14*x^84 + 41*x^83 + 100*x^82 + 79*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 19*x^75 + 52*x^74 + 37*x^73 + 6*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 34*x^68 + 87*x^67 + 44*x^66 + 81*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 73*x^27 + 44*x^26 + 127*x^25 + 34*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 6*x^20 + 13*x^19 + 52*x^18 + 75*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 119*x^11 + 100*x^10 + 97*x^9 + 14*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 58*x^4 + 11*x^3 + 124*x^2 + 125*x + 110, x^95 + 15*x^93 + 94*x^92 + 69*x^91 + 76*x^90 + 35*x^89 + 26*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 94*x^84 + 57*x^83 + 84*x^82 + 127*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 35*x^75 + 36*x^74 + 85*x^73 + 102*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 18*x^68 + 7*x^67 + 124*x^66 + 97*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 57*x^27 + 60*x^26 + 79*x^25 + 2*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 22*x^20 + 93*x^19 + 100*x^18 + 59*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 71*x^11 + 20*x^10 + 81*x^9 + 110*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 106*x^4 + 123*x^3 + 12*x^2 + 77*x + 46, x^95 + 15*x^93 + 50*x^92 + 53*x^91 + 4*x^90 + 51*x^89 + 38*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 18*x^84 + 9*x^83 + 28*x^82 + 47*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 115*x^75 + 76*x^74 + 5*x^73 + 26*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 62*x^68 + 119*x^67 + 84*x^66 + 113*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 105*x^27 + 84*x^26 + 31*x^25 + 62*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 26*x^20 + 109*x^19 + 76*x^18 + 43*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 87*x^11 + 28*x^10 + 65*x^9 + 18*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 38*x^4 + 43*x^3 + 4*x^2 + 29*x + 50, x^95 + 15*x^93 + 106*x^92 + 117*x^91 + 100*x^90 + 83*x^89 + 126*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 106*x^84 + 73*x^83 + 124*x^82 + 15*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 51*x^75 + 108*x^74 + 101*x^73 + 2*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 102*x^68 + 55*x^67 + 116*x^66 + 17*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 41*x^27 + 52*x^26 + 63*x^25 + 118*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 82*x^20 + 45*x^19 + 44*x^18 + 11*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 23*x^11 + 60*x^10 + 33*x^9 + 90*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 46*x^4 + 107*x^3 + 36*x^2 + 61*x + 26, x^95 + 15*x^93 + 110*x^92 + 53*x^91 + 92*x^90 + 115*x^89 + 90*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 78*x^84 + 9*x^83 + 4*x^82 + 111*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 115*x^75 + 84*x^74 + 69*x^73 + 102*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 98*x^68 + 119*x^67 + 12*x^66 + 49*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 105*x^27 + 12*x^26 + 95*x^25 + 66*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 70*x^20 + 109*x^19 + 84*x^18 + 107*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 87*x^11 + 4*x^10 + x^9 + 110*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 122*x^4 + 43*x^3 + 92*x^2 + 93*x + 14, x^95 + 15*x^93 + 126*x^92 + 101*x^91 + 12*x^90 + 67*x^89 + 58*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 126*x^84 + 25*x^83 + 20*x^82 + 95*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 3*x^75 + 100*x^74 + 53*x^73 + 70*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 114*x^68 + 39*x^67 + 60*x^66 + x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 89*x^27 + 124*x^26 + 111*x^25 + 34*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 54*x^20 + 61*x^19 + 36*x^18 + 27*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 39*x^11 + 84*x^10 + 49*x^9 + 78*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 74*x^4 + 27*x^3 + 76*x^2 + 109*x + 14, x^95 + 15*x^93 + 10*x^92 + 117*x^91 + 100*x^90 + 83*x^89 + 30*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 10*x^84 + 73*x^83 + 124*x^82 + 15*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 51*x^75 + 108*x^74 + 101*x^73 + 98*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 70*x^68 + 55*x^67 + 116*x^66 + 17*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 41*x^27 + 52*x^26 + 63*x^25 + 22*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 114*x^20 + 45*x^19 + 44*x^18 + 11*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 23*x^11 + 60*x^10 + 33*x^9 + 58*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 14*x^4 + 107*x^3 + 36*x^2 + 61*x + 122, x^95 + 15*x^93 + 14*x^92 + 69*x^91 + 12*x^90 + 99*x^89 + 10*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 78*x^84 + 57*x^83 + 20*x^82 + 63*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 35*x^75 + 100*x^74 + 21*x^73 + 118*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 34*x^68 + 7*x^67 + 60*x^66 + 33*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 57*x^27 + 124*x^26 + 15*x^25 + 50*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 70*x^20 + 93*x^19 + 36*x^18 + 123*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 71*x^11 + 84*x^10 + 17*x^9 + 62*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 58*x^4 + 123*x^3 + 76*x^2 + 13*x + 62, x^95 + 15*x^93 + 26*x^92 + 69*x^91 + 116*x^90 + 3*x^89 + 30*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 122*x^84 + 57*x^83 + 44*x^82 + 31*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 35*x^75 + 28*x^74 + 117*x^73 + 34*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 22*x^68 + 7*x^67 + 4*x^66 + 65*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 57*x^27 + 4*x^26 + 47*x^25 + 22*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 34*x^20 + 93*x^19 + 28*x^18 + 91*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 71*x^11 + 44*x^10 + 113*x^9 + 122*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 30*x^4 + 123*x^3 + 116*x^2 + 45*x + 26, x^95 + 15*x^93 + 14*x^92 + 69*x^91 + 44*x^90 + 35*x^89 + 42*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 14*x^84 + 57*x^83 + 116*x^82 + 127*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 35*x^75 + 68*x^74 + 85*x^73 + 86*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 98*x^68 + 7*x^67 + 92*x^66 + 97*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 57*x^27 + 28*x^26 + 79*x^25 + 82*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 6*x^20 + 93*x^19 + 4*x^18 + 59*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 71*x^11 + 52*x^10 + 81*x^9 + 30*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 122*x^4 + 123*x^3 + 108*x^2 + 77*x + 94, x^95 + 15*x^93 + 86*x^92 + 5*x^91 + 76*x^90 + 67*x^89 + 82*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 54*x^84 + 121*x^83 + 20*x^82 + 95*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 99*x^75 + 36*x^74 + 53*x^73 + 110*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 58*x^68 + 71*x^67 + 60*x^66 + x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 121*x^27 + 60*x^26 + 111*x^25 + 26*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 78*x^20 + 29*x^19 + 36*x^18 + 27*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 7*x^11 + 20*x^10 + 49*x^9 + 86*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 114*x^4 + 59*x^3 + 76*x^2 + 109*x + 118, x^95 + 15*x^93 + 58*x^92 + 117*x^91 + 68*x^90 + 19*x^89 + 110*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 58*x^84 + 73*x^83 + 28*x^82 + 79*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 51*x^75 + 12*x^74 + 37*x^73 + 18*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 22*x^68 + 55*x^67 + 84*x^66 + 81*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 41*x^27 + 20*x^26 + 127*x^25 + 38*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 98*x^20 + 45*x^19 + 76*x^18 + 75*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 23*x^11 + 92*x^10 + 97*x^9 + 42*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 30*x^4 + 107*x^3 + 4*x^2 + 125*x + 106, x^95 + 15*x^93 + 122*x^92 + 37*x^91 + 20*x^90 + 99*x^89 + 30*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 26*x^84 + 89*x^83 + 12*x^82 + 63*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 67*x^75 + 124*x^74 + 21*x^73 + 34*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 118*x^68 + 103*x^67 + 36*x^66 + 33*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 25*x^27 + 36*x^26 + 15*x^25 + 22*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 66*x^20 + 125*x^19 + 124*x^18 + 123*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 103*x^11 + 12*x^10 + 17*x^9 + 122*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 126*x^4 + 91*x^3 + 20*x^2 + 13*x + 90, x^95 + 15*x^93 + 54*x^92 + 117*x^91 + 28*x^90 + 19*x^89 + 98*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 54*x^84 + 73*x^83 + 4*x^82 + 79*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 51*x^75 + 20*x^74 + 37*x^73 + 30*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 122*x^68 + 55*x^67 + 12*x^66 + 81*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 41*x^27 + 76*x^26 + 127*x^25 + 106*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 78*x^20 + 45*x^19 + 84*x^18 + 75*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 23*x^11 + 68*x^10 + 97*x^9 + 70*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 50*x^4 + 107*x^3 + 92*x^2 + 125*x + 6, x^95 + 15*x^93 + 70*x^92 + 85*x^91 + 28*x^90 + 115*x^89 + 114*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 6*x^84 + 105*x^83 + 4*x^82 + 111*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 83*x^75 + 20*x^74 + 69*x^73 + 14*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 42*x^68 + 23*x^67 + 12*x^66 + 49*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 9*x^27 + 76*x^26 + 95*x^25 + 58*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 94*x^20 + 77*x^19 + 84*x^18 + 107*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 55*x^11 + 68*x^10 + x^9 + 118*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 34*x^4 + 75*x^3 + 92*x^2 + 93*x + 118, x^95 + 15*x^93 + 122*x^92 + 101*x^91 + 52*x^90 + 35*x^89 + 126*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 90*x^84 + 25*x^83 + 108*x^82 + 127*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 3*x^75 + 92*x^74 + 85*x^73 + 66*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 54*x^68 + 39*x^67 + 68*x^66 + 97*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 89*x^27 + 68*x^26 + 79*x^25 + 118*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 2*x^20 + 61*x^19 + 92*x^18 + 59*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 39*x^11 + 108*x^10 + 81*x^9 + 26*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 62*x^4 + 27*x^3 + 52*x^2 + 77*x + 58, x^95 + 15*x^93 + 26*x^92 + 53*x^91 + 68*x^90 + 83*x^89 + 78*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 26*x^84 + 9*x^83 + 28*x^82 + 15*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 115*x^75 + 12*x^74 + 101*x^73 + 50*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 54*x^68 + 119*x^67 + 84*x^66 + 17*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 105*x^27 + 20*x^26 + 63*x^25 + 6*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 66*x^20 + 109*x^19 + 76*x^18 + 11*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 87*x^11 + 92*x^10 + 33*x^9 + 74*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 62*x^4 + 43*x^3 + 4*x^2 + 61*x + 10, x^95 + 15*x^93 + 114*x^92 + 85*x^91 + 4*x^90 + 19*x^89 + 102*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 82*x^84 + 105*x^83 + 28*x^82 + 79*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 83*x^75 + 76*x^74 + 37*x^73 + 90*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 126*x^68 + 23*x^67 + 84*x^66 + 81*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 9*x^27 + 84*x^26 + 127*x^25 + 126*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 90*x^20 + 77*x^19 + 76*x^18 + 75*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 55*x^11 + 28*x^10 + 97*x^9 + 82*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 102*x^4 + 75*x^3 + 4*x^2 + 125*x + 114, x^95 + 15*x^93 + 42*x^92 + 69*x^91 + 84*x^90 + 67*x^89 + 78*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 10*x^84 + 57*x^83 + 76*x^82 + 95*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 35*x^75 + 60*x^74 + 53*x^73 + 114*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 6*x^68 + 7*x^67 + 100*x^66 + x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 57*x^27 + 100*x^26 + 111*x^25 + 6*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 114*x^20 + 93*x^19 + 60*x^18 + 27*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 71*x^11 + 76*x^10 + 49*x^9 + 10*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 78*x^4 + 123*x^3 + 84*x^2 + 109*x + 42, x^95 + 15*x^93 + 62*x^92 + 101*x^91 + 108*x^90 + 67*x^89 + 26*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 126*x^84 + 25*x^83 + 52*x^82 + 95*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 3*x^75 + 4*x^74 + 53*x^73 + 102*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 114*x^68 + 39*x^67 + 28*x^66 + x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 89*x^27 + 92*x^26 + 111*x^25 + 2*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 54*x^20 + 61*x^19 + 68*x^18 + 27*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 39*x^11 + 116*x^10 + 49*x^9 + 110*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 74*x^4 + 27*x^3 + 44*x^2 + 109*x + 110, x^95 + 15*x^93 + 38*x^92 + 21*x^91 + 92*x^90 + 115*x^89 + 82*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 102*x^84 + 41*x^83 + 68*x^82 + 111*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 19*x^75 + 84*x^74 + 69*x^73 + 46*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 74*x^68 + 87*x^67 + 76*x^66 + 49*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 73*x^27 + 12*x^26 + 95*x^25 + 26*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 62*x^20 + 13*x^19 + 20*x^18 + 107*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 119*x^11 + 4*x^10 + x^9 + 22*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 66*x^4 + 11*x^3 + 28*x^2 + 93*x + 22, x^95 + 15*x^93 + 62*x^92 + 37*x^91 + 108*x^90 + 3*x^89 + 26*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 126*x^84 + 89*x^83 + 52*x^82 + 31*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 67*x^75 + 4*x^74 + 117*x^73 + 102*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 114*x^68 + 103*x^67 + 28*x^66 + 65*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 25*x^27 + 92*x^26 + 47*x^25 + 2*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 54*x^20 + 125*x^19 + 68*x^18 + 91*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 103*x^11 + 116*x^10 + 113*x^9 + 110*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 74*x^4 + 91*x^3 + 44*x^2 + 45*x + 110, x^95 + 15*x^93 + 2*x^92 + 21*x^91 + 36*x^90 + 83*x^89 + 22*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 98*x^84 + 41*x^83 + 124*x^82 + 15*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 19*x^75 + 44*x^74 + 101*x^73 + 42*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 110*x^68 + 87*x^67 + 116*x^66 + 17*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 73*x^27 + 116*x^26 + 63*x^25 + 110*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 42*x^20 + 13*x^19 + 44*x^18 + 11*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 119*x^11 + 124*x^10 + 33*x^9 + 98*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 22*x^4 + 11*x^3 + 36*x^2 + 61*x + 2, x^95 + 15*x^93 + 118*x^92 + 37*x^91 + 44*x^90 + 99*x^89 + 82*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 22*x^84 + 89*x^83 + 52*x^82 + 63*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 67*x^75 + 68*x^74 + 21*x^73 + 110*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 90*x^68 + 103*x^67 + 28*x^66 + 33*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 25*x^27 + 28*x^26 + 15*x^25 + 26*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 46*x^20 + 125*x^19 + 68*x^18 + 123*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 103*x^11 + 52*x^10 + 17*x^9 + 86*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 18*x^4 + 91*x^3 + 44*x^2 + 13*x + 54, x^95 + 15*x^93 + 42*x^92 + 101*x^91 + 20*x^90 + 35*x^89 + 14*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 10*x^84 + 25*x^83 + 12*x^82 + 127*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 3*x^75 + 124*x^74 + 85*x^73 + 50*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 6*x^68 + 39*x^67 + 36*x^66 + 97*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 89*x^27 + 36*x^26 + 79*x^25 + 70*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 114*x^20 + 61*x^19 + 124*x^18 + 59*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 39*x^11 + 12*x^10 + 81*x^9 + 74*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 78*x^4 + 27*x^3 + 20*x^2 + 77*x + 106, x^95 + 15*x^93 + 94*x^92 + 21*x^91 + 28*x^90 + 19*x^89 + 74*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 126*x^84 + 41*x^83 + 68*x^82 + 79*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 19*x^75 + 20*x^74 + 37*x^73 + 118*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 50*x^68 + 87*x^67 + 76*x^66 + 81*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 73*x^27 + 76*x^26 + 127*x^25 + 114*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 54*x^20 + 13*x^19 + 20*x^18 + 75*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 119*x^11 + 68*x^10 + 97*x^9 + 62*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 10*x^4 + 11*x^3 + 28*x^2 + 125*x + 30, x^95 + 15*x^93 + 2*x^92 + 117*x^91 + 36*x^90 + 51*x^89 + 86*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 98*x^84 + 73*x^83 + 124*x^82 + 47*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 51*x^75 + 44*x^74 + 5*x^73 + 106*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 110*x^68 + 55*x^67 + 116*x^66 + 113*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 41*x^27 + 116*x^26 + 31*x^25 + 46*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 42*x^20 + 45*x^19 + 44*x^18 + 43*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 23*x^11 + 124*x^10 + 65*x^9 + 34*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 22*x^4 + 107*x^3 + 36*x^2 + 29*x + 66, x^95 + 15*x^93 + 50*x^92 + 69*x^91 + 116*x^90 + 35*x^89 + 118*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 114*x^84 + 57*x^83 + 108*x^82 + 127*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 35*x^75 + 28*x^74 + 85*x^73 + 10*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 30*x^68 + 7*x^67 + 68*x^66 + 97*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 57*x^27 + 4*x^26 + 79*x^25 + 78*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 122*x^20 + 93*x^19 + 92*x^18 + 59*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 71*x^11 + 44*x^10 + 81*x^9 + 66*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 6*x^4 + 123*x^3 + 52*x^2 + 77*x + 66, x^95 + 15*x^93 + 118*x^92 + 85*x^91 + 124*x^90 + 51*x^89 + 66*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 54*x^84 + 105*x^83 + 36*x^82 + 47*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 83*x^75 + 52*x^74 + 5*x^73 + 62*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 122*x^68 + 23*x^67 + 108*x^66 + 113*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 9*x^27 + 44*x^26 + 31*x^25 + 74*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 78*x^20 + 77*x^19 + 116*x^18 + 43*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 55*x^11 + 100*x^10 + 65*x^9 + 102*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 50*x^4 + 75*x^3 + 60*x^2 + 29*x + 102, x^95 + 15*x^93 + 82*x^92 + 101*x^91 + 84*x^90 + 67*x^89 + 118*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 82*x^84 + 25*x^83 + 12*x^82 + 95*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 3*x^75 + 60*x^74 + 53*x^73 + 10*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 62*x^68 + 39*x^67 + 36*x^66 + x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 89*x^27 + 100*x^26 + 111*x^25 + 78*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 90*x^20 + 61*x^19 + 124*x^18 + 27*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 39*x^11 + 76*x^10 + 49*x^9 + 66*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 38*x^4 + 27*x^3 + 20*x^2 + 109*x + 2, x^95 + 15*x^93 + 82*x^92 + 21*x^91 + 4*x^90 + 83*x^89 + 70*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 50*x^84 + 41*x^83 + 28*x^82 + 15*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 19*x^75 + 76*x^74 + 101*x^73 + 122*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 30*x^68 + 87*x^67 + 84*x^66 + 17*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 73*x^27 + 84*x^26 + 63*x^25 + 94*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 58*x^20 + 13*x^19 + 76*x^18 + 11*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 119*x^11 + 28*x^10 + 33*x^9 + 114*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 6*x^4 + 11*x^3 + 4*x^2 + 61*x + 18, x^95 + 15*x^93 + 78*x^92 + 117*x^91 + 28*x^90 + 115*x^89 + 58*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 46*x^84 + 73*x^83 + 68*x^82 + 111*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 51*x^75 + 20*x^74 + 69*x^73 + 6*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 2*x^68 + 55*x^67 + 76*x^66 + 49*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 41*x^27 + 76*x^26 + 95*x^25 + 34*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 38*x^20 + 45*x^19 + 20*x^18 + 107*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 23*x^11 + 68*x^10 + x^9 + 14*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 26*x^4 + 107*x^3 + 28*x^2 + 93*x + 46, x^95 + 15*x^93 + 86*x^92 + 37*x^91 + 44*x^90 + 99*x^89 + 50*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 118*x^84 + 89*x^83 + 52*x^82 + 63*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 67*x^75 + 68*x^74 + 21*x^73 + 14*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 122*x^68 + 103*x^67 + 28*x^66 + 33*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 25*x^27 + 28*x^26 + 15*x^25 + 122*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 14*x^20 + 125*x^19 + 68*x^18 + 123*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 103*x^11 + 52*x^10 + 17*x^9 + 118*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 50*x^4 + 91*x^3 + 44*x^2 + 13*x + 86, x^95 + 15*x^93 + 50*x^92 + 117*x^91 + 4*x^90 + 51*x^89 + 102*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 18*x^84 + 73*x^83 + 28*x^82 + 47*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 51*x^75 + 76*x^74 + 5*x^73 + 90*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 62*x^68 + 55*x^67 + 84*x^66 + 113*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 41*x^27 + 84*x^26 + 31*x^25 + 126*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 26*x^20 + 45*x^19 + 76*x^18 + 43*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 23*x^11 + 28*x^10 + 65*x^9 + 82*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 38*x^4 + 107*x^3 + 4*x^2 + 29*x + 114, x^95 + 15*x^93 + 110*x^92 + 101*x^91 + 44*x^90 + 3*x^89 + 10*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 110*x^84 + 25*x^83 + 116*x^82 + 31*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 3*x^75 + 68*x^74 + 117*x^73 + 118*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 2*x^68 + 39*x^67 + 92*x^66 + 65*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 89*x^27 + 28*x^26 + 47*x^25 + 50*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 102*x^20 + 61*x^19 + 4*x^18 + 91*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 39*x^11 + 52*x^10 + 113*x^9 + 62*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 26*x^4 + 27*x^3 + 108*x^2 + 45*x + 126, x^95 + 15*x^93 + 82*x^92 + 21*x^91 + 36*x^90 + 19*x^89 + 102*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 114*x^84 + 41*x^83 + 124*x^82 + 79*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 19*x^75 + 44*x^74 + 37*x^73 + 90*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 94*x^68 + 87*x^67 + 116*x^66 + 81*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 73*x^27 + 116*x^26 + 127*x^25 + 126*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 122*x^20 + 13*x^19 + 44*x^18 + 75*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 119*x^11 + 124*x^10 + 97*x^9 + 82*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 70*x^4 + 11*x^3 + 36*x^2 + 125*x + 50, x^95 + 15*x^93 + 78*x^92 + 101*x^91 + 108*x^90 + 67*x^89 + 106*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 78*x^84 + 25*x^83 + 52*x^82 + 95*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 3*x^75 + 4*x^74 + 53*x^73 + 22*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 34*x^68 + 39*x^67 + 28*x^66 + x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 89*x^27 + 92*x^26 + 111*x^25 + 18*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 70*x^20 + 61*x^19 + 68*x^18 + 27*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 39*x^11 + 116*x^10 + 49*x^9 + 94*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 58*x^4 + 27*x^3 + 44*x^2 + 109*x + 30, x^95 + 15*x^93 + 30*x^92 + 117*x^91 + 60*x^90 + 115*x^89 + 42*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 126*x^84 + 73*x^83 + 36*x^82 + 111*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 51*x^75 + 116*x^74 + 69*x^73 + 22*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 50*x^68 + 55*x^67 + 108*x^66 + 49*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 41*x^27 + 108*x^26 + 95*x^25 + 82*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 54*x^20 + 45*x^19 + 116*x^18 + 107*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 23*x^11 + 36*x^10 + x^9 + 94*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 10*x^4 + 107*x^3 + 60*x^2 + 93*x + 126, x^95 + 15*x^93 + 30*x^92 + 21*x^91 + 28*x^90 + 83*x^89 + 74*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 62*x^84 + 41*x^83 + 68*x^82 + 15*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 19*x^75 + 20*x^74 + 101*x^73 + 118*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 114*x^68 + 87*x^67 + 76*x^66 + 17*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 73*x^27 + 76*x^26 + 63*x^25 + 114*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 118*x^20 + 13*x^19 + 20*x^18 + 11*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 119*x^11 + 68*x^10 + 33*x^9 + 62*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 74*x^4 + 11*x^3 + 28*x^2 + 61*x + 30, x^95 + 15*x^93 + 30*x^92 + 37*x^91 + 44*x^90 + 67*x^89 + 122*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 94*x^84 + 89*x^83 + 116*x^82 + 95*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 67*x^75 + 68*x^74 + 53*x^73 + 6*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 18*x^68 + 103*x^67 + 92*x^66 + x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 25*x^27 + 28*x^26 + 111*x^25 + 98*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 22*x^20 + 125*x^19 + 4*x^18 + 27*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 103*x^11 + 52*x^10 + 49*x^9 + 14*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 106*x^4 + 91*x^3 + 108*x^2 + 109*x + 14, x^95 + 15*x^93 + 10*x^92 + 21*x^91 + 36*x^90 + 51*x^89 + 94*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 10*x^84 + 41*x^83 + 60*x^82 + 47*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 19*x^75 + 44*x^74 + 5*x^73 + 34*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 70*x^68 + 87*x^67 + 52*x^66 + 113*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 73*x^27 + 116*x^26 + 31*x^25 + 86*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 114*x^20 + 13*x^19 + 108*x^18 + 43*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 119*x^11 + 124*x^10 + 65*x^9 + 122*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 14*x^4 + 11*x^3 + 100*x^2 + 29*x + 58, x^95 + 15*x^93 + 30*x^92 + 69*x^91 + 12*x^90 + 99*x^89 + 90*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 30*x^84 + 57*x^83 + 20*x^82 + 63*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 35*x^75 + 100*x^74 + 21*x^73 + 38*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 82*x^68 + 7*x^67 + 60*x^66 + 33*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 57*x^27 + 124*x^26 + 15*x^25 + 66*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 86*x^20 + 93*x^19 + 36*x^18 + 123*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 71*x^11 + 84*x^10 + 17*x^9 + 46*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 42*x^4 + 123*x^3 + 76*x^2 + 13*x + 110, x^95 + 15*x^93 + 10*x^92 + 21*x^91 + 100*x^90 + 51*x^89 + 30*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 10*x^84 + 41*x^83 + 124*x^82 + 47*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 19*x^75 + 108*x^74 + 5*x^73 + 98*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 70*x^68 + 87*x^67 + 116*x^66 + 113*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 73*x^27 + 52*x^26 + 31*x^25 + 22*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 114*x^20 + 13*x^19 + 44*x^18 + 43*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 119*x^11 + 60*x^10 + 65*x^9 + 58*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 14*x^4 + 11*x^3 + 36*x^2 + 29*x + 122, x^95 + 15*x^93 + 54*x^92 + 101*x^91 + 44*x^90 + 99*x^89 + 82*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 86*x^84 + 25*x^83 + 52*x^82 + 63*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 3*x^75 + 68*x^74 + 21*x^73 + 110*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 26*x^68 + 39*x^67 + 28*x^66 + 33*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 89*x^27 + 28*x^26 + 15*x^25 + 26*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 110*x^20 + 61*x^19 + 68*x^18 + 123*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 39*x^11 + 52*x^10 + 17*x^9 + 86*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 82*x^4 + 27*x^3 + 44*x^2 + 13*x + 54, x^95 + 15*x^93 + 70*x^92 + 101*x^91 + 12*x^90 + 35*x^89 + 2*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 102*x^84 + 25*x^83 + 84*x^82 + 127*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 3*x^75 + 100*x^74 + 85*x^73 + 62*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 10*x^68 + 39*x^67 + 124*x^66 + 97*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 89*x^27 + 124*x^26 + 79*x^25 + 10*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 62*x^20 + 61*x^19 + 100*x^18 + 59*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 39*x^11 + 84*x^10 + 81*x^9 + 102*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 2*x^4 + 27*x^3 + 12*x^2 + 77*x + 70, x^95 + 15*x^93 + 54*x^92 + 101*x^91 + 12*x^90 + 35*x^89 + 50*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 22*x^84 + 25*x^83 + 84*x^82 + 127*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 3*x^75 + 100*x^74 + 85*x^73 + 14*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 90*x^68 + 39*x^67 + 124*x^66 + 97*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 89*x^27 + 124*x^26 + 79*x^25 + 122*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 46*x^20 + 61*x^19 + 100*x^18 + 59*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 39*x^11 + 84*x^10 + 81*x^9 + 118*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 18*x^4 + 27*x^3 + 12*x^2 + 77*x + 22, x^95 + 15*x^93 + 122*x^92 + 5*x^91 + 20*x^90 + 3*x^89 + 30*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 26*x^84 + 121*x^83 + 12*x^82 + 31*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 99*x^75 + 124*x^74 + 117*x^73 + 34*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 118*x^68 + 71*x^67 + 36*x^66 + 65*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 121*x^27 + 36*x^26 + 47*x^25 + 22*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 66*x^20 + 29*x^19 + 124*x^18 + 91*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 7*x^11 + 12*x^10 + 113*x^9 + 122*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 126*x^4 + 59*x^3 + 20*x^2 + 45*x + 90, x^95 + 15*x^93 + 42*x^92 + 69*x^91 + 52*x^90 + 3*x^89 + 46*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 74*x^84 + 57*x^83 + 108*x^82 + 31*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 35*x^75 + 92*x^74 + 117*x^73 + 18*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 70*x^68 + 7*x^67 + 68*x^66 + 65*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 57*x^27 + 68*x^26 + 47*x^25 + 102*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 50*x^20 + 93*x^19 + 92*x^18 + 91*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 71*x^11 + 108*x^10 + 113*x^9 + 42*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 14*x^4 + 123*x^3 + 52*x^2 + 45*x + 10, x^95 + 15*x^93 + 98*x^92 + 53*x^91 + 68*x^90 + 115*x^89 + 22*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 2*x^84 + 9*x^83 + 92*x^82 + 111*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 115*x^75 + 12*x^74 + 69*x^73 + 42*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 78*x^68 + 119*x^67 + 20*x^66 + 49*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 105*x^27 + 20*x^26 + 95*x^25 + 110*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 74*x^20 + 109*x^19 + 12*x^18 + 107*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 87*x^11 + 92*x^10 + x^9 + 98*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 118*x^4 + 43*x^3 + 68*x^2 + 93*x + 66, x^95 + 15*x^93 + 6*x^92 + 85*x^91 + 28*x^90 + 51*x^89 + 114*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 70*x^84 + 105*x^83 + 4*x^82 + 47*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 83*x^75 + 20*x^74 + 5*x^73 + 14*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 106*x^68 + 23*x^67 + 12*x^66 + 113*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 9*x^27 + 76*x^26 + 31*x^25 + 58*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 30*x^20 + 77*x^19 + 84*x^18 + 43*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 55*x^11 + 68*x^10 + 65*x^9 + 118*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 98*x^4 + 75*x^3 + 92*x^2 + 29*x + 118, x^95 + 15*x^93 + 70*x^92 + 21*x^91 + 124*x^90 + 51*x^89 + 18*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 70*x^84 + 41*x^83 + 36*x^82 + 47*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 19*x^75 + 52*x^74 + 5*x^73 + 110*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 106*x^68 + 87*x^67 + 108*x^66 + 113*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 73*x^27 + 44*x^26 + 31*x^25 + 90*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 30*x^20 + 13*x^19 + 116*x^18 + 43*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 119*x^11 + 100*x^10 + 65*x^9 + 86*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 98*x^4 + 11*x^3 + 60*x^2 + 29*x + 22, x^95 + 15*x^93 + 126*x^92 + 37*x^91 + 76*x^90 + 3*x^89 + 122*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 126*x^84 + 89*x^83 + 84*x^82 + 31*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 67*x^75 + 36*x^74 + 117*x^73 + 6*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 114*x^68 + 103*x^67 + 124*x^66 + 65*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 25*x^27 + 60*x^26 + 47*x^25 + 98*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 54*x^20 + 125*x^19 + 100*x^18 + 91*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 103*x^11 + 20*x^10 + 113*x^9 + 14*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 74*x^4 + 91*x^3 + 12*x^2 + 45*x + 78, x^95 + 15*x^93 + 34*x^92 + 21*x^91 + 4*x^90 + 83*x^89 + 86*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 66*x^84 + 41*x^83 + 28*x^82 + 15*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 19*x^75 + 76*x^74 + 101*x^73 + 106*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 14*x^68 + 87*x^67 + 84*x^66 + 17*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 73*x^27 + 84*x^26 + 63*x^25 + 46*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 10*x^20 + 13*x^19 + 76*x^18 + 11*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 119*x^11 + 28*x^10 + 33*x^9 + 34*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 54*x^4 + 11*x^3 + 4*x^2 + 61*x + 2, x^95 + 15*x^93 + 34*x^92 + 85*x^91 + 100*x^90 + 19*x^89 + 118*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 2*x^84 + 105*x^83 + 60*x^82 + 79*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 83*x^75 + 108*x^74 + 37*x^73 + 74*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 78*x^68 + 23*x^67 + 52*x^66 + 81*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 9*x^27 + 52*x^26 + 127*x^25 + 78*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 74*x^20 + 77*x^19 + 108*x^18 + 75*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 55*x^11 + 60*x^10 + 97*x^9 + 2*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 118*x^4 + 75*x^3 + 100*x^2 + 125*x + 34, x^95 + 15*x^93 + 126*x^92 + 101*x^91 + 76*x^90 + 3*x^89 + 58*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 126*x^84 + 25*x^83 + 84*x^82 + 31*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 3*x^75 + 36*x^74 + 117*x^73 + 70*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 114*x^68 + 39*x^67 + 124*x^66 + 65*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 89*x^27 + 60*x^26 + 47*x^25 + 34*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 54*x^20 + 61*x^19 + 100*x^18 + 91*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 39*x^11 + 20*x^10 + 113*x^9 + 78*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 74*x^4 + 27*x^3 + 12*x^2 + 45*x + 14, x^95 + 15*x^93 + 38*x^92 + 5*x^91 + 12*x^90 + 67*x^89 + 34*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 70*x^84 + 121*x^83 + 84*x^82 + 95*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 99*x^75 + 100*x^74 + 53*x^73 + 30*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 42*x^68 + 71*x^67 + 124*x^66 + x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 121*x^27 + 124*x^26 + 111*x^25 + 42*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 30*x^20 + 29*x^19 + 100*x^18 + 27*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 7*x^11 + 84*x^10 + 49*x^9 + 70*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 34*x^4 + 59*x^3 + 12*x^2 + 109*x + 38, x^95 + 15*x^93 + 106*x^92 + 53*x^91 + 100*x^90 + 83*x^89 + 62*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 106*x^84 + 9*x^83 + 124*x^82 + 15*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 115*x^75 + 108*x^74 + 101*x^73 + 66*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 102*x^68 + 119*x^67 + 116*x^66 + 17*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 105*x^27 + 52*x^26 + 63*x^25 + 54*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 82*x^20 + 109*x^19 + 44*x^18 + 11*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 87*x^11 + 60*x^10 + 33*x^9 + 26*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 46*x^4 + 43*x^3 + 36*x^2 + 61*x + 90, x^95 + 15*x^93 + 42*x^92 + 85*x^91 + 36*x^90 + 115*x^89 + 126*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 42*x^84 + 105*x^83 + 60*x^82 + 111*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 83*x^75 + 44*x^74 + 69*x^73 + 2*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 38*x^68 + 23*x^67 + 52*x^66 + 49*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 9*x^27 + 116*x^26 + 95*x^25 + 118*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 18*x^20 + 77*x^19 + 108*x^18 + 107*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 55*x^11 + 124*x^10 + x^9 + 90*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 110*x^4 + 75*x^3 + 100*x^2 + 93*x + 26, x^95 + 15*x^93 + 78*x^92 + 37*x^91 + 108*x^90 + 3*x^89 + 106*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 78*x^84 + 89*x^83 + 52*x^82 + 31*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 67*x^75 + 4*x^74 + 117*x^73 + 22*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 34*x^68 + 103*x^67 + 28*x^66 + 65*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 25*x^27 + 92*x^26 + 47*x^25 + 18*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 70*x^20 + 125*x^19 + 68*x^18 + 91*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 103*x^11 + 116*x^10 + 113*x^9 + 94*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 58*x^4 + 91*x^3 + 44*x^2 + 45*x + 30, x^95 + 15*x^93 + 2*x^92 + 101*x^91 + 84*x^90 + 3*x^89 + 38*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 66*x^84 + 25*x^83 + 12*x^82 + 31*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 3*x^75 + 60*x^74 + 117*x^73 + 90*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 78*x^68 + 39*x^67 + 36*x^66 + 65*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 89*x^27 + 100*x^26 + 47*x^25 + 62*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 10*x^20 + 61*x^19 + 124*x^18 + 91*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 39*x^11 + 76*x^10 + 113*x^9 + 82*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 118*x^4 + 27*x^3 + 20*x^2 + 45*x + 82, x^95 + 15*x^93 + 90*x^92 + 21*x^91 + 36*x^90 + 115*x^89 + 46*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 26*x^84 + 41*x^83 + 60*x^82 + 111*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 19*x^75 + 44*x^74 + 69*x^73 + 82*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 54*x^68 + 87*x^67 + 52*x^66 + 49*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 73*x^27 + 116*x^26 + 95*x^25 + 102*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 66*x^20 + 13*x^19 + 108*x^18 + 107*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 119*x^11 + 124*x^10 + x^9 + 106*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 62*x^4 + 11*x^3 + 100*x^2 + 93*x + 106, x^95 + 15*x^93 + 126*x^92 + 117*x^91 + 60*x^90 + 51*x^89 + 74*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 94*x^84 + 73*x^83 + 36*x^82 + 47*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 51*x^75 + 116*x^74 + 5*x^73 + 118*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 82*x^68 + 55*x^67 + 108*x^66 + 113*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 41*x^27 + 108*x^26 + 31*x^25 + 114*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 22*x^20 + 45*x^19 + 116*x^18 + 43*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 23*x^11 + 36*x^10 + 65*x^9 + 62*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 42*x^4 + 107*x^3 + 60*x^2 + 29*x + 94, x^95 + 15*x^93 + 2*x^92 + 53*x^91 + 68*x^90 + 51*x^89 + 118*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 34*x^84 + 9*x^83 + 92*x^82 + 47*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 115*x^75 + 12*x^74 + 5*x^73 + 74*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 46*x^68 + 119*x^67 + 20*x^66 + 113*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 105*x^27 + 20*x^26 + 31*x^25 + 78*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 106*x^20 + 109*x^19 + 12*x^18 + 43*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 87*x^11 + 92*x^10 + 65*x^9 + 2*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 86*x^4 + 43*x^3 + 68*x^2 + 29*x + 98, x^95 + 15*x^93 + 18*x^92 + 101*x^91 + 52*x^90 + 3*x^89 + 22*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 82*x^84 + 25*x^83 + 44*x^82 + 31*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 3*x^75 + 92*x^74 + 117*x^73 + 106*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 62*x^68 + 39*x^67 + 4*x^66 + 65*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 89*x^27 + 68*x^26 + 47*x^25 + 110*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 90*x^20 + 61*x^19 + 28*x^18 + 91*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 39*x^11 + 108*x^10 + 113*x^9 + 34*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 38*x^4 + 27*x^3 + 116*x^2 + 45*x + 34, x^95 + 15*x^93 + 58*x^92 + 53*x^91 + 68*x^90 + 19*x^89 + 46*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 58*x^84 + 9*x^83 + 28*x^82 + 79*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 115*x^75 + 12*x^74 + 37*x^73 + 82*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 22*x^68 + 119*x^67 + 84*x^66 + 81*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 105*x^27 + 20*x^26 + 127*x^25 + 102*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 98*x^20 + 109*x^19 + 76*x^18 + 75*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 87*x^11 + 92*x^10 + 97*x^9 + 106*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 30*x^4 + 43*x^3 + 4*x^2 + 125*x + 42, x^95 + 15*x^93 + 110*x^92 + 85*x^91 + 124*x^90 + 19*x^89 + 122*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 14*x^84 + 105*x^83 + 100*x^82 + 79*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 83*x^75 + 52*x^74 + 37*x^73 + 70*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 34*x^68 + 23*x^67 + 44*x^66 + 81*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 9*x^27 + 44*x^26 + 127*x^25 + 98*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 6*x^20 + 77*x^19 + 52*x^18 + 75*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 55*x^11 + 100*x^10 + 97*x^9 + 78*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 58*x^4 + 75*x^3 + 124*x^2 + 125*x + 46, x^95 + 15*x^93 + 86*x^92 + 53*x^91 + 60*x^90 + 83*x^89 + 98*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 22*x^84 + 9*x^83 + 100*x^82 + 15*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 115*x^75 + 116*x^74 + 101*x^73 + 30*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 26*x^68 + 119*x^67 + 44*x^66 + 17*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 105*x^27 + 108*x^26 + 63*x^25 + 106*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 46*x^20 + 109*x^19 + 52*x^18 + 11*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 87*x^11 + 36*x^10 + 33*x^9 + 70*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 82*x^4 + 43*x^3 + 124*x^2 + 61*x + 70, x^95 + 15*x^93 + 86*x^92 + 37*x^91 + 12*x^90 + 35*x^89 + 18*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 54*x^84 + 89*x^83 + 84*x^82 + 127*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 67*x^75 + 100*x^74 + 85*x^73 + 46*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 58*x^68 + 103*x^67 + 124*x^66 + 97*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 25*x^27 + 124*x^26 + 79*x^25 + 90*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 78*x^20 + 125*x^19 + 100*x^18 + 59*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 103*x^11 + 84*x^10 + 81*x^9 + 22*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 114*x^4 + 91*x^3 + 12*x^2 + 77*x + 54, x^95 + 15*x^93 + 102*x^92 + 21*x^91 + 60*x^90 + 115*x^89 + 50*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 102*x^84 + 41*x^83 + 100*x^82 + 111*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 19*x^75 + 116*x^74 + 69*x^73 + 78*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 74*x^68 + 87*x^67 + 44*x^66 + 49*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 73*x^27 + 108*x^26 + 95*x^25 + 122*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 62*x^20 + 13*x^19 + 52*x^18 + 107*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 119*x^11 + 36*x^10 + x^9 + 54*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 66*x^4 + 11*x^3 + 124*x^2 + 93*x + 118, x^95 + 15*x^93 + 94*x^92 + 53*x^91 + 28*x^90 + 51*x^89 + 10*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 126*x^84 + 9*x^83 + 68*x^82 + 47*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 115*x^75 + 20*x^74 + 5*x^73 + 54*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 50*x^68 + 119*x^67 + 76*x^66 + 113*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 105*x^27 + 76*x^26 + 31*x^25 + 50*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 54*x^20 + 109*x^19 + 20*x^18 + 43*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 87*x^11 + 68*x^10 + 65*x^9 + 126*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 10*x^4 + 43*x^3 + 28*x^2 + 29*x + 94, x^95 + 15*x^93 + 58*x^92 + 101*x^91 + 20*x^90 + 35*x^89 + 94*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 90*x^84 + 25*x^83 + 12*x^82 + 127*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 3*x^75 + 124*x^74 + 85*x^73 + 98*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 54*x^68 + 39*x^67 + 36*x^66 + 97*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 89*x^27 + 36*x^26 + 79*x^25 + 86*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 2*x^20 + 61*x^19 + 124*x^18 + 59*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 39*x^11 + 12*x^10 + 81*x^9 + 58*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 62*x^4 + 27*x^3 + 20*x^2 + 77*x + 26, x^95 + 15*x^93 + 110*x^92 + 117*x^91 + 92*x^90 + 115*x^89 + 26*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 78*x^84 + 73*x^83 + 4*x^82 + 111*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 51*x^75 + 84*x^74 + 69*x^73 + 38*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 98*x^68 + 55*x^67 + 12*x^66 + 49*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 41*x^27 + 12*x^26 + 95*x^25 + 2*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 70*x^20 + 45*x^19 + 84*x^18 + 107*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 23*x^11 + 4*x^10 + x^9 + 46*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 122*x^4 + 107*x^3 + 92*x^2 + 93*x + 78, x^95 + 15*x^93 + 6*x^92 + 5*x^91 + 12*x^90 + 67*x^89 + 2*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 38*x^84 + 121*x^83 + 84*x^82 + 95*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 99*x^75 + 100*x^74 + 53*x^73 + 62*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 74*x^68 + 71*x^67 + 124*x^66 + x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 121*x^27 + 124*x^26 + 111*x^25 + 10*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 126*x^20 + 29*x^19 + 100*x^18 + 27*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 7*x^11 + 84*x^10 + 49*x^9 + 102*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 66*x^4 + 59*x^3 + 12*x^2 + 109*x + 70, x^95 + 15*x^93 + 50*x^92 + 53*x^91 + 36*x^90 + 115*x^89 + 70*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 82*x^84 + 9*x^83 + 124*x^82 + 111*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 115*x^75 + 44*x^74 + 69*x^73 + 122*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 126*x^68 + 119*x^67 + 116*x^66 + 49*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 105*x^27 + 116*x^26 + 95*x^25 + 94*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 90*x^20 + 109*x^19 + 44*x^18 + 107*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 87*x^11 + 124*x^10 + x^9 + 114*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 102*x^4 + 43*x^3 + 36*x^2 + 93*x + 82, x^95 + 15*x^93 + 46*x^92 + 69*x^91 + 76*x^90 + 99*x^89 + 106*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 110*x^84 + 57*x^83 + 84*x^82 + 63*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 35*x^75 + 36*x^74 + 21*x^73 + 22*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 2*x^68 + 7*x^67 + 124*x^66 + 33*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 57*x^27 + 60*x^26 + 15*x^25 + 18*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 102*x^20 + 93*x^19 + 100*x^18 + 123*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 71*x^11 + 20*x^10 + 17*x^9 + 94*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 26*x^4 + 123*x^3 + 12*x^2 + 13*x + 94, x^95 + 15*x^93 + 26*x^92 + 53*x^91 + 4*x^90 + 83*x^89 + 14*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 26*x^84 + 9*x^83 + 92*x^82 + 15*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 115*x^75 + 76*x^74 + 101*x^73 + 114*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 54*x^68 + 119*x^67 + 20*x^66 + 17*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 105*x^27 + 84*x^26 + 63*x^25 + 70*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 66*x^20 + 109*x^19 + 12*x^18 + 11*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 87*x^11 + 28*x^10 + 33*x^9 + 10*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 62*x^4 + 43*x^3 + 68*x^2 + 61*x + 74, x^95 + 15*x^93 + 122*x^92 + 69*x^91 + 20*x^90 + 67*x^89 + 30*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 26*x^84 + 57*x^83 + 12*x^82 + 95*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 35*x^75 + 124*x^74 + 53*x^73 + 34*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 118*x^68 + 7*x^67 + 36*x^66 + x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 57*x^27 + 36*x^26 + 111*x^25 + 22*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 66*x^20 + 93*x^19 + 124*x^18 + 27*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 71*x^11 + 12*x^10 + 49*x^9 + 122*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 126*x^4 + 123*x^3 + 20*x^2 + 109*x + 90, x^95 + 15*x^93 + 6*x^92 + 37*x^91 + 44*x^90 + 99*x^89 + 34*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 102*x^84 + 89*x^83 + 52*x^82 + 63*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 67*x^75 + 68*x^74 + 21*x^73 + 30*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 10*x^68 + 103*x^67 + 28*x^66 + 33*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 25*x^27 + 28*x^26 + 15*x^25 + 42*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 62*x^20 + 125*x^19 + 68*x^18 + 123*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 103*x^11 + 52*x^10 + 17*x^9 + 70*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 2*x^4 + 91*x^3 + 44*x^2 + 13*x + 102, x^95 + 15*x^93 + 86*x^92 + 101*x^91 + 108*x^90 + 35*x^89 + 114*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 118*x^84 + 25*x^83 + 116*x^82 + 127*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 3*x^75 + 4*x^74 + 85*x^73 + 78*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 122*x^68 + 39*x^67 + 92*x^66 + 97*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 89*x^27 + 92*x^26 + 79*x^25 + 58*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 14*x^20 + 61*x^19 + 4*x^18 + 59*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 39*x^11 + 116*x^10 + 81*x^9 + 54*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 50*x^4 + 27*x^3 + 108*x^2 + 77*x + 22, x^95 + 15*x^93 + 14*x^92 + 85*x^91 + 124*x^90 + 83*x^89 + 90*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 46*x^84 + 105*x^83 + 100*x^82 + 15*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 83*x^75 + 52*x^74 + 101*x^73 + 102*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 2*x^68 + 23*x^67 + 44*x^66 + 17*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 9*x^27 + 44*x^26 + 63*x^25 + 66*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 38*x^20 + 77*x^19 + 52*x^18 + 11*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 55*x^11 + 100*x^10 + 33*x^9 + 110*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 26*x^4 + 75*x^3 + 124*x^2 + 61*x + 78, x^95 + 15*x^93 + 38*x^92 + 21*x^91 + 60*x^90 + 115*x^89 + 114*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 38*x^84 + 41*x^83 + 100*x^82 + 111*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 19*x^75 + 116*x^74 + 69*x^73 + 14*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 10*x^68 + 87*x^67 + 44*x^66 + 49*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 73*x^27 + 108*x^26 + 95*x^25 + 58*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 126*x^20 + 13*x^19 + 52*x^18 + 107*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 119*x^11 + 36*x^10 + x^9 + 118*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 2*x^4 + 11*x^3 + 124*x^2 + 93*x + 54, x^95 + 15*x^93 + 46*x^92 + 117*x^91 + 28*x^90 + 115*x^89 + 26*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 14*x^84 + 73*x^83 + 68*x^82 + 111*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 51*x^75 + 20*x^74 + 69*x^73 + 38*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 34*x^68 + 55*x^67 + 76*x^66 + 49*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 41*x^27 + 76*x^26 + 95*x^25 + 2*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 6*x^20 + 45*x^19 + 20*x^18 + 107*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 23*x^11 + 68*x^10 + x^9 + 46*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 58*x^4 + 107*x^3 + 28*x^2 + 93*x + 78, x^95 + 15*x^93 + 14*x^92 + 85*x^91 + 92*x^90 + 19*x^89 + 58*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 110*x^84 + 105*x^83 + 4*x^82 + 79*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 83*x^75 + 84*x^74 + 37*x^73 + 6*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 66*x^68 + 23*x^67 + 12*x^66 + 81*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 9*x^27 + 12*x^26 + 127*x^25 + 34*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 102*x^20 + 77*x^19 + 84*x^18 + 75*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 55*x^11 + 4*x^10 + 97*x^9 + 14*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 90*x^4 + 75*x^3 + 92*x^2 + 125*x + 46, x^95 + 15*x^93 + 18*x^92 + 117*x^91 + 4*x^90 + 115*x^89 + 6*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 114*x^84 + 73*x^83 + 28*x^82 + 111*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 51*x^75 + 76*x^74 + 69*x^73 + 58*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 94*x^68 + 55*x^67 + 84*x^66 + 49*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 41*x^27 + 84*x^26 + 95*x^25 + 30*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 122*x^20 + 45*x^19 + 76*x^18 + 107*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 23*x^11 + 28*x^10 + x^9 + 50*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 70*x^4 + 107*x^3 + 4*x^2 + 93*x + 82, x^95 + 15*x^93 + 66*x^92 + 21*x^91 + 100*x^90 + 19*x^89 + 86*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 34*x^84 + 41*x^83 + 60*x^82 + 79*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 19*x^75 + 108*x^74 + 37*x^73 + 106*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 46*x^68 + 87*x^67 + 52*x^66 + 81*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 73*x^27 + 52*x^26 + 127*x^25 + 46*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 106*x^20 + 13*x^19 + 108*x^18 + 75*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 119*x^11 + 60*x^10 + 97*x^9 + 34*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 86*x^4 + 11*x^3 + 100*x^2 + 125*x + 66, x^95 + 15*x^93 + 70*x^92 + 85*x^91 + 60*x^90 + 51*x^89 + 18*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 70*x^84 + 105*x^83 + 100*x^82 + 47*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 83*x^75 + 116*x^74 + 5*x^73 + 110*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 106*x^68 + 23*x^67 + 44*x^66 + 113*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 9*x^27 + 108*x^26 + 31*x^25 + 90*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 30*x^20 + 77*x^19 + 52*x^18 + 43*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 55*x^11 + 36*x^10 + 65*x^9 + 86*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 98*x^4 + 75*x^3 + 124*x^2 + 29*x + 22, x^95 + 15*x^93 + 110*x^92 + 117*x^91 + 92*x^90 + 51*x^89 + 90*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 78*x^84 + 73*x^83 + 4*x^82 + 47*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 51*x^75 + 84*x^74 + 5*x^73 + 102*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 98*x^68 + 55*x^67 + 12*x^66 + 113*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 41*x^27 + 12*x^26 + 31*x^25 + 66*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 70*x^20 + 45*x^19 + 84*x^18 + 43*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 23*x^11 + 4*x^10 + 65*x^9 + 110*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 122*x^4 + 107*x^3 + 92*x^2 + 29*x + 14, x^95 + 15*x^93 + 34*x^92 + 37*x^91 + 52*x^90 + 67*x^89 + 102*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 34*x^84 + 89*x^83 + 44*x^82 + 95*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 67*x^75 + 92*x^74 + 53*x^73 + 26*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 110*x^68 + 103*x^67 + 4*x^66 + x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 25*x^27 + 68*x^26 + 111*x^25 + 126*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 106*x^20 + 125*x^19 + 28*x^18 + 27*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 103*x^11 + 108*x^10 + 49*x^9 + 18*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 22*x^4 + 91*x^3 + 116*x^2 + 109*x + 82, x^95 + 15*x^93 + 50*x^92 + 101*x^91 + 52*x^90 + 67*x^89 + 118*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 114*x^84 + 25*x^83 + 44*x^82 + 95*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 3*x^75 + 92*x^74 + 53*x^73 + 10*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 30*x^68 + 39*x^67 + 4*x^66 + x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 89*x^27 + 68*x^26 + 111*x^25 + 78*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 122*x^20 + 61*x^19 + 28*x^18 + 27*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 39*x^11 + 108*x^10 + 49*x^9 + 66*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 6*x^4 + 27*x^3 + 116*x^2 + 109*x + 66, x^95 + 15*x^93 + 118*x^92 + 69*x^91 + 44*x^90 + 67*x^89 + 82*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 22*x^84 + 57*x^83 + 52*x^82 + 95*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 35*x^75 + 68*x^74 + 53*x^73 + 110*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 90*x^68 + 7*x^67 + 28*x^66 + x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 57*x^27 + 28*x^26 + 111*x^25 + 26*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 46*x^20 + 93*x^19 + 68*x^18 + 27*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 71*x^11 + 52*x^10 + 49*x^9 + 86*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 18*x^4 + 123*x^3 + 44*x^2 + 109*x + 54, x^95 + 15*x^93 + 30*x^92 + 37*x^91 + 108*x^90 + 3*x^89 + 122*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 94*x^84 + 89*x^83 + 52*x^82 + 31*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 67*x^75 + 4*x^74 + 117*x^73 + 6*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 18*x^68 + 103*x^67 + 28*x^66 + 65*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 25*x^27 + 92*x^26 + 47*x^25 + 98*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 22*x^20 + 125*x^19 + 68*x^18 + 91*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 103*x^11 + 116*x^10 + 113*x^9 + 14*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 106*x^4 + 91*x^3 + 44*x^2 + 45*x + 14, x^95 + 15*x^93 + 14*x^92 + 101*x^91 + 76*x^90 + 67*x^89 + 74*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 78*x^84 + 25*x^83 + 84*x^82 + 95*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 3*x^75 + 36*x^74 + 53*x^73 + 54*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 34*x^68 + 39*x^67 + 124*x^66 + x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 89*x^27 + 60*x^26 + 111*x^25 + 114*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 70*x^20 + 61*x^19 + 100*x^18 + 27*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 39*x^11 + 20*x^10 + 49*x^9 + 126*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 58*x^4 + 27*x^3 + 12*x^2 + 109*x + 126, x^95 + 15*x^93 + 82*x^92 + 5*x^91 + 52*x^90 + 99*x^89 + 86*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 18*x^84 + 121*x^83 + 44*x^82 + 63*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 99*x^75 + 92*x^74 + 21*x^73 + 42*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 126*x^68 + 71*x^67 + 4*x^66 + 33*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 121*x^27 + 68*x^26 + 15*x^25 + 46*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 26*x^20 + 29*x^19 + 28*x^18 + 123*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 7*x^11 + 108*x^10 + 17*x^9 + 98*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 102*x^4 + 59*x^3 + 116*x^2 + 13*x + 98, x^95 + 15*x^93 + 54*x^92 + 101*x^91 + 44*x^90 + 35*x^89 + 18*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 86*x^84 + 25*x^83 + 52*x^82 + 127*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 3*x^75 + 68*x^74 + 85*x^73 + 46*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 26*x^68 + 39*x^67 + 28*x^66 + 97*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 89*x^27 + 28*x^26 + 79*x^25 + 90*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 110*x^20 + 61*x^19 + 68*x^18 + 59*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 39*x^11 + 52*x^10 + 81*x^9 + 22*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 82*x^4 + 27*x^3 + 44*x^2 + 77*x + 118, x^95 + 15*x^93 + 102*x^92 + 69*x^91 + 44*x^90 + 3*x^89 + 66*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 70*x^84 + 57*x^83 + 52*x^82 + 31*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 35*x^75 + 68*x^74 + 117*x^73 + 126*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 42*x^68 + 7*x^67 + 28*x^66 + 65*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 57*x^27 + 28*x^26 + 47*x^25 + 74*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 30*x^20 + 93*x^19 + 68*x^18 + 91*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 71*x^11 + 52*x^10 + 113*x^9 + 38*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 34*x^4 + 123*x^3 + 44*x^2 + 45*x + 70, x^95 + 15*x^93 + 118*x^92 + 53*x^91 + 60*x^90 + 83*x^89 + 2*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 54*x^84 + 9*x^83 + 100*x^82 + 15*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 115*x^75 + 116*x^74 + 101*x^73 + 126*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 122*x^68 + 119*x^67 + 44*x^66 + 17*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 105*x^27 + 108*x^26 + 63*x^25 + 10*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 78*x^20 + 109*x^19 + 52*x^18 + 11*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 87*x^11 + 36*x^10 + 33*x^9 + 38*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 50*x^4 + 43*x^3 + 124*x^2 + 61*x + 38, x^95 + 15*x^93 + 98*x^92 + 101*x^91 + 52*x^90 + 67*x^89 + 102*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 98*x^84 + 25*x^83 + 44*x^82 + 95*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 3*x^75 + 92*x^74 + 53*x^73 + 26*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 46*x^68 + 39*x^67 + 4*x^66 + x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 89*x^27 + 68*x^26 + 111*x^25 + 126*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 42*x^20 + 61*x^19 + 28*x^18 + 27*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 39*x^11 + 108*x^10 + 49*x^9 + 18*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 86*x^4 + 27*x^3 + 116*x^2 + 109*x + 82, x^95 + 15*x^93 + 14*x^92 + 21*x^91 + 124*x^90 + 19*x^89 + 90*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 46*x^84 + 41*x^83 + 100*x^82 + 79*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 19*x^75 + 52*x^74 + 37*x^73 + 102*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 2*x^68 + 87*x^67 + 44*x^66 + 81*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 73*x^27 + 44*x^26 + 127*x^25 + 66*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 38*x^20 + 13*x^19 + 52*x^18 + 75*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 119*x^11 + 100*x^10 + 97*x^9 + 110*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 26*x^4 + 11*x^3 + 124*x^2 + 125*x + 78, x^95 + 15*x^93 + 66*x^92 + 5*x^91 + 20*x^90 + 35*x^89 + 102*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 2*x^84 + 121*x^83 + 76*x^82 + 127*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 99*x^75 + 124*x^74 + 85*x^73 + 26*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 14*x^68 + 71*x^67 + 100*x^66 + 97*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 121*x^27 + 36*x^26 + 79*x^25 + 126*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 74*x^20 + 29*x^19 + 60*x^18 + 59*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 7*x^11 + 12*x^10 + 81*x^9 + 18*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 54*x^4 + 59*x^3 + 84*x^2 + 77*x + 18, x^95 + 15*x^93 + 42*x^92 + 37*x^91 + 52*x^90 + 35*x^89 + 46*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 74*x^84 + 89*x^83 + 108*x^82 + 127*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 67*x^75 + 92*x^74 + 85*x^73 + 18*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 70*x^68 + 103*x^67 + 68*x^66 + 97*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 25*x^27 + 68*x^26 + 79*x^25 + 102*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 50*x^20 + 125*x^19 + 92*x^18 + 59*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 103*x^11 + 108*x^10 + 81*x^9 + 42*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 14*x^4 + 91*x^3 + 52*x^2 + 77*x + 10, x^95 + 15*x^93 + 66*x^92 + 85*x^91 + 36*x^90 + 19*x^89 + 86*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 34*x^84 + 105*x^83 + 124*x^82 + 79*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 83*x^75 + 44*x^74 + 37*x^73 + 106*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 46*x^68 + 23*x^67 + 116*x^66 + 81*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 9*x^27 + 116*x^26 + 127*x^25 + 46*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 106*x^20 + 77*x^19 + 44*x^18 + 75*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 55*x^11 + 124*x^10 + 97*x^9 + 34*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 86*x^4 + 75*x^3 + 36*x^2 + 125*x + 66, x^95 + 15*x^93 + 10*x^92 + 5*x^91 + 20*x^90 + 67*x^89 + 46*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 106*x^84 + 121*x^83 + 12*x^82 + 95*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 99*x^75 + 124*x^74 + 53*x^73 + 18*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 38*x^68 + 71*x^67 + 36*x^66 + x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 121*x^27 + 36*x^26 + 111*x^25 + 102*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 82*x^20 + 29*x^19 + 124*x^18 + 27*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 7*x^11 + 12*x^10 + 49*x^9 + 42*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 110*x^4 + 59*x^3 + 20*x^2 + 109*x + 74, x^95 + 15*x^93 + 34*x^92 + 69*x^91 + 116*x^90 + 35*x^89 + 38*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 34*x^84 + 57*x^83 + 108*x^82 + 127*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 35*x^75 + 28*x^74 + 85*x^73 + 90*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 110*x^68 + 7*x^67 + 68*x^66 + 97*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 57*x^27 + 4*x^26 + 79*x^25 + 62*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 106*x^20 + 93*x^19 + 92*x^18 + 59*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 71*x^11 + 44*x^10 + 81*x^9 + 82*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 22*x^4 + 123*x^3 + 52*x^2 + 77*x + 18, x^95 + 15*x^93 + 122*x^92 + 69*x^91 + 20*x^90 + 3*x^89 + 94*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 26*x^84 + 57*x^83 + 12*x^82 + 31*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 35*x^75 + 124*x^74 + 117*x^73 + 98*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 118*x^68 + 7*x^67 + 36*x^66 + 65*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 57*x^27 + 36*x^26 + 47*x^25 + 86*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 66*x^20 + 93*x^19 + 124*x^18 + 91*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 71*x^11 + 12*x^10 + 113*x^9 + 58*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 126*x^4 + 123*x^3 + 20*x^2 + 45*x + 26, x^95 + 15*x^93 + 126*x^92 + 69*x^91 + 12*x^90 + 35*x^89 + 122*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 126*x^84 + 57*x^83 + 20*x^82 + 127*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 35*x^75 + 100*x^74 + 85*x^73 + 6*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 114*x^68 + 7*x^67 + 60*x^66 + 97*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 57*x^27 + 124*x^26 + 79*x^25 + 98*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 54*x^20 + 93*x^19 + 36*x^18 + 59*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 71*x^11 + 84*x^10 + 81*x^9 + 14*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 74*x^4 + 123*x^3 + 76*x^2 + 77*x + 78, x^95 + 15*x^93 + 74*x^92 + 69*x^91 + 116*x^90 + 67*x^89 + 78*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 106*x^84 + 57*x^83 + 44*x^82 + 95*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 35*x^75 + 28*x^74 + 53*x^73 + 114*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 38*x^68 + 7*x^67 + 4*x^66 + x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 57*x^27 + 4*x^26 + 111*x^25 + 6*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 82*x^20 + 93*x^19 + 28*x^18 + 27*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 71*x^11 + 44*x^10 + 49*x^9 + 10*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 110*x^4 + 123*x^3 + 116*x^2 + 109*x + 106, x^95 + 15*x^93 + 74*x^92 + 85*x^91 + 36*x^90 + 51*x^89 + 94*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 74*x^84 + 105*x^83 + 60*x^82 + 47*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 83*x^75 + 44*x^74 + 5*x^73 + 34*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 6*x^68 + 23*x^67 + 52*x^66 + 113*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 9*x^27 + 116*x^26 + 31*x^25 + 86*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 50*x^20 + 77*x^19 + 108*x^18 + 43*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 55*x^11 + 124*x^10 + 65*x^9 + 122*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 78*x^4 + 75*x^3 + 100*x^2 + 29*x + 58, x^95 + 15*x^93 + 34*x^92 + 101*x^91 + 20*x^90 + 3*x^89 + 6*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 98*x^84 + 25*x^83 + 76*x^82 + 31*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 3*x^75 + 124*x^74 + 117*x^73 + 122*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 46*x^68 + 39*x^67 + 100*x^66 + 65*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 89*x^27 + 36*x^26 + 47*x^25 + 30*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 42*x^20 + 61*x^19 + 60*x^18 + 91*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 39*x^11 + 12*x^10 + 113*x^9 + 114*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 86*x^4 + 27*x^3 + 84*x^2 + 45*x + 114, x^95 + 15*x^93 + 70*x^92 + 37*x^91 + 44*x^90 + 35*x^89 + 34*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 38*x^84 + 89*x^83 + 52*x^82 + 127*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 67*x^75 + 68*x^74 + 85*x^73 + 30*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 74*x^68 + 103*x^67 + 28*x^66 + 97*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 25*x^27 + 28*x^26 + 79*x^25 + 42*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 126*x^20 + 125*x^19 + 68*x^18 + 59*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 103*x^11 + 52*x^10 + 81*x^9 + 70*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 66*x^4 + 91*x^3 + 44*x^2 + 77*x + 102, x^95 + 15*x^93 + 90*x^92 + 21*x^91 + 100*x^90 + 115*x^89 + 110*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 26*x^84 + 41*x^83 + 124*x^82 + 111*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 19*x^75 + 108*x^74 + 69*x^73 + 18*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 54*x^68 + 87*x^67 + 116*x^66 + 49*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 73*x^27 + 52*x^26 + 95*x^25 + 38*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 66*x^20 + 13*x^19 + 44*x^18 + 107*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 119*x^11 + 60*x^10 + x^9 + 42*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 62*x^4 + 11*x^3 + 36*x^2 + 93*x + 42, x^95 + 15*x^93 + 118*x^92 + 117*x^91 + 92*x^90 + 19*x^89 + 98*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 118*x^84 + 73*x^83 + 68*x^82 + 79*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 51*x^75 + 84*x^74 + 37*x^73 + 30*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 58*x^68 + 55*x^67 + 76*x^66 + 81*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 41*x^27 + 12*x^26 + 127*x^25 + 106*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 14*x^20 + 45*x^19 + 20*x^18 + 75*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 23*x^11 + 4*x^10 + 97*x^9 + 70*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 114*x^4 + 107*x^3 + 28*x^2 + 125*x + 6, x^95 + 15*x^93 + 18*x^92 + 21*x^91 + 68*x^90 + 19*x^89 + 6*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 114*x^84 + 41*x^83 + 92*x^82 + 79*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 19*x^75 + 12*x^74 + 37*x^73 + 58*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 94*x^68 + 87*x^67 + 20*x^66 + 81*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 73*x^27 + 20*x^26 + 127*x^25 + 30*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 122*x^20 + 13*x^19 + 12*x^18 + 75*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 119*x^11 + 92*x^10 + 97*x^9 + 50*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 70*x^4 + 11*x^3 + 68*x^2 + 125*x + 82, x^95 + 15*x^93 + 62*x^92 + 117*x^91 + 60*x^90 + 115*x^89 + 74*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 30*x^84 + 73*x^83 + 36*x^82 + 111*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 51*x^75 + 116*x^74 + 69*x^73 + 118*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 18*x^68 + 55*x^67 + 108*x^66 + 49*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 41*x^27 + 108*x^26 + 95*x^25 + 114*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 86*x^20 + 45*x^19 + 116*x^18 + 107*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 23*x^11 + 36*x^10 + x^9 + 62*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 106*x^4 + 107*x^3 + 60*x^2 + 93*x + 94, x^95 + 15*x^93 + 58*x^92 + 37*x^91 + 52*x^90 + 35*x^89 + 126*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 26*x^84 + 89*x^83 + 108*x^82 + 127*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 67*x^75 + 92*x^74 + 85*x^73 + 66*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 118*x^68 + 103*x^67 + 68*x^66 + 97*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 25*x^27 + 68*x^26 + 79*x^25 + 118*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 66*x^20 + 125*x^19 + 92*x^18 + 59*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 103*x^11 + 108*x^10 + 81*x^9 + 26*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 126*x^4 + 91*x^3 + 52*x^2 + 77*x + 58, x^95 + 15*x^93 + 90*x^92 + 37*x^91 + 20*x^90 + 99*x^89 + 126*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 122*x^84 + 89*x^83 + 12*x^82 + 63*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 67*x^75 + 124*x^74 + 21*x^73 + 66*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 22*x^68 + 103*x^67 + 36*x^66 + 33*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 25*x^27 + 36*x^26 + 15*x^25 + 118*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 34*x^20 + 125*x^19 + 124*x^18 + 123*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 103*x^11 + 12*x^10 + 17*x^9 + 26*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 30*x^4 + 91*x^3 + 20*x^2 + 13*x + 122, x^95 + 15*x^93 + 10*x^92 + 5*x^91 + 52*x^90 + 3*x^89 + 78*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 42*x^84 + 121*x^83 + 108*x^82 + 31*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 99*x^75 + 92*x^74 + 117*x^73 + 114*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 102*x^68 + 71*x^67 + 68*x^66 + 65*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 121*x^27 + 68*x^26 + 47*x^25 + 6*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 18*x^20 + 29*x^19 + 92*x^18 + 91*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 7*x^11 + 108*x^10 + 113*x^9 + 10*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 46*x^4 + 59*x^3 + 52*x^2 + 45*x + 106, x^95 + 15*x^93 + 114*x^92 + 53*x^91 + 68*x^90 + 51*x^89 + 38*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 82*x^84 + 9*x^83 + 92*x^82 + 47*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 115*x^75 + 12*x^74 + 5*x^73 + 26*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 126*x^68 + 119*x^67 + 20*x^66 + 113*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 105*x^27 + 20*x^26 + 31*x^25 + 62*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 90*x^20 + 109*x^19 + 12*x^18 + 43*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 87*x^11 + 92*x^10 + 65*x^9 + 18*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 102*x^4 + 43*x^3 + 68*x^2 + 29*x + 50, x^95 + 15*x^93 + 46*x^92 + 53*x^91 + 28*x^90 + 115*x^89 + 90*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 14*x^84 + 9*x^83 + 68*x^82 + 111*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 115*x^75 + 20*x^74 + 69*x^73 + 102*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 34*x^68 + 119*x^67 + 76*x^66 + 49*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 105*x^27 + 76*x^26 + 95*x^25 + 66*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 6*x^20 + 109*x^19 + 20*x^18 + 107*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 87*x^11 + 68*x^10 + x^9 + 110*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 58*x^4 + 43*x^3 + 28*x^2 + 93*x + 14, x^95 + 15*x^93 + 106*x^92 + 37*x^91 + 84*x^90 + 35*x^89 + 78*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 74*x^84 + 89*x^83 + 76*x^82 + 127*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 67*x^75 + 60*x^74 + 85*x^73 + 114*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 70*x^68 + 103*x^67 + 100*x^66 + 97*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 25*x^27 + 100*x^26 + 79*x^25 + 6*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 50*x^20 + 125*x^19 + 60*x^18 + 59*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 103*x^11 + 76*x^10 + 81*x^9 + 10*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 14*x^4 + 91*x^3 + 84*x^2 + 77*x + 42, x^95 + 15*x^93 + 6*x^92 + 85*x^91 + 92*x^90 + 51*x^89 + 50*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 70*x^84 + 105*x^83 + 68*x^82 + 47*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 83*x^75 + 84*x^74 + 5*x^73 + 78*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 106*x^68 + 23*x^67 + 76*x^66 + 113*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 9*x^27 + 12*x^26 + 31*x^25 + 122*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 30*x^20 + 77*x^19 + 20*x^18 + 43*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 55*x^11 + 4*x^10 + 65*x^9 + 54*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 98*x^4 + 75*x^3 + 28*x^2 + 29*x + 54, x^95 + 15*x^93 + 78*x^92 + 21*x^91 + 28*x^90 + 83*x^89 + 58*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 46*x^84 + 41*x^83 + 68*x^82 + 15*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 19*x^75 + 20*x^74 + 101*x^73 + 6*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 2*x^68 + 87*x^67 + 76*x^66 + 17*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 73*x^27 + 76*x^26 + 63*x^25 + 34*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 38*x^20 + 13*x^19 + 20*x^18 + 11*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 119*x^11 + 68*x^10 + 33*x^9 + 14*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 26*x^4 + 11*x^3 + 28*x^2 + 61*x + 46, x^95 + 15*x^93 + 46*x^92 + 37*x^91 + 76*x^90 + 67*x^89 + 42*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 110*x^84 + 89*x^83 + 84*x^82 + 95*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 67*x^75 + 36*x^74 + 53*x^73 + 86*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 2*x^68 + 103*x^67 + 124*x^66 + x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 25*x^27 + 60*x^26 + 111*x^25 + 82*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 102*x^20 + 125*x^19 + 100*x^18 + 27*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 103*x^11 + 20*x^10 + 49*x^9 + 30*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 26*x^4 + 91*x^3 + 12*x^2 + 109*x + 30, x^95 + 15*x^93 + 78*x^92 + 53*x^91 + 124*x^90 + 115*x^89 + 26*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 110*x^84 + 9*x^83 + 100*x^82 + 111*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 115*x^75 + 52*x^74 + 69*x^73 + 38*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 66*x^68 + 119*x^67 + 44*x^66 + 49*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 105*x^27 + 44*x^26 + 95*x^25 + 2*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 102*x^20 + 109*x^19 + 52*x^18 + 107*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 87*x^11 + 100*x^10 + x^9 + 46*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 90*x^4 + 43*x^3 + 124*x^2 + 93*x + 14, x^95 + 15*x^93 + 6*x^92 + 21*x^91 + 124*x^90 + 115*x^89 + 18*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 6*x^84 + 41*x^83 + 36*x^82 + 111*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 19*x^75 + 52*x^74 + 69*x^73 + 110*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 42*x^68 + 87*x^67 + 108*x^66 + 49*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 73*x^27 + 44*x^26 + 95*x^25 + 90*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 94*x^20 + 13*x^19 + 116*x^18 + 107*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 119*x^11 + 100*x^10 + x^9 + 86*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 34*x^4 + 11*x^3 + 60*x^2 + 93*x + 22, x^95 + 15*x^93 + 42*x^92 + 101*x^91 + 116*x^90 + 35*x^89 + 46*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 74*x^84 + 25*x^83 + 44*x^82 + 127*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 3*x^75 + 28*x^74 + 85*x^73 + 18*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 70*x^68 + 39*x^67 + 4*x^66 + 97*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 89*x^27 + 4*x^26 + 79*x^25 + 102*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 50*x^20 + 61*x^19 + 28*x^18 + 59*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 39*x^11 + 44*x^10 + 81*x^9 + 42*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 14*x^4 + 27*x^3 + 116*x^2 + 77*x + 10, x^95 + 15*x^93 + 34*x^92 + 5*x^91 + 84*x^90 + 99*x^89 + 70*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 98*x^84 + 121*x^83 + 12*x^82 + 63*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 99*x^75 + 60*x^74 + 21*x^73 + 58*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 46*x^68 + 71*x^67 + 36*x^66 + 33*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 121*x^27 + 100*x^26 + 15*x^25 + 94*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 42*x^20 + 29*x^19 + 124*x^18 + 123*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 7*x^11 + 76*x^10 + 17*x^9 + 50*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 86*x^4 + 59*x^3 + 20*x^2 + 13*x + 50, x^95 + 15*x^93 + 14*x^92 + 21*x^91 + 92*x^90 + 19*x^89 + 122*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 110*x^84 + 41*x^83 + 4*x^82 + 79*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 19*x^75 + 84*x^74 + 37*x^73 + 70*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 66*x^68 + 87*x^67 + 12*x^66 + 81*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 73*x^27 + 12*x^26 + 127*x^25 + 98*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 102*x^20 + 13*x^19 + 84*x^18 + 75*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 119*x^11 + 4*x^10 + 97*x^9 + 78*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 90*x^4 + 11*x^3 + 92*x^2 + 125*x + 110, x^95 + 15*x^93 + 110*x^92 + 101*x^91 + 44*x^90 + 67*x^89 + 74*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 110*x^84 + 25*x^83 + 116*x^82 + 95*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 3*x^75 + 68*x^74 + 53*x^73 + 54*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 2*x^68 + 39*x^67 + 92*x^66 + x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 89*x^27 + 28*x^26 + 111*x^25 + 114*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 102*x^20 + 61*x^19 + 4*x^18 + 27*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 39*x^11 + 52*x^10 + 49*x^9 + 126*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 26*x^4 + 27*x^3 + 108*x^2 + 109*x + 62, x^95 + 15*x^93 + 94*x^92 + 37*x^91 + 76*x^90 + 3*x^89 + 90*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 94*x^84 + 89*x^83 + 84*x^82 + 31*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 67*x^75 + 36*x^74 + 117*x^73 + 38*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 18*x^68 + 103*x^67 + 124*x^66 + 65*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 25*x^27 + 60*x^26 + 47*x^25 + 66*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 22*x^20 + 125*x^19 + 100*x^18 + 91*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 103*x^11 + 20*x^10 + 113*x^9 + 46*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 106*x^4 + 91*x^3 + 12*x^2 + 45*x + 110, x^95 + 15*x^93 + 98*x^92 + 37*x^91 + 84*x^90 + 3*x^89 + 70*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 34*x^84 + 89*x^83 + 12*x^82 + 31*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 67*x^75 + 60*x^74 + 117*x^73 + 58*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 110*x^68 + 103*x^67 + 36*x^66 + 65*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 25*x^27 + 100*x^26 + 47*x^25 + 94*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 106*x^20 + 125*x^19 + 124*x^18 + 91*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 103*x^11 + 76*x^10 + 113*x^9 + 50*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 22*x^4 + 91*x^3 + 20*x^2 + 45*x + 50, x^95 + 15*x^93 + 102*x^92 + 117*x^91 + 60*x^90 + 83*x^89 + 114*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 102*x^84 + 73*x^83 + 100*x^82 + 15*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 51*x^75 + 116*x^74 + 101*x^73 + 14*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 74*x^68 + 55*x^67 + 44*x^66 + 17*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 41*x^27 + 108*x^26 + 63*x^25 + 58*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 62*x^20 + 45*x^19 + 52*x^18 + 11*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 23*x^11 + 36*x^10 + 33*x^9 + 118*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 66*x^4 + 107*x^3 + 124*x^2 + 61*x + 54, x^95 + 15*x^93 + 10*x^92 + 21*x^91 + 4*x^90 + 51*x^89 + 126*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 74*x^84 + 41*x^83 + 92*x^82 + 47*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 19*x^75 + 76*x^74 + 5*x^73 + 2*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 6*x^68 + 87*x^67 + 20*x^66 + 113*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 73*x^27 + 84*x^26 + 31*x^25 + 118*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 50*x^20 + 13*x^19 + 12*x^18 + 43*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 119*x^11 + 28*x^10 + 65*x^9 + 90*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 78*x^4 + 11*x^3 + 68*x^2 + 29*x + 90, x^95 + 15*x^93 + 86*x^92 + 101*x^91 + 76*x^90 + 99*x^89 + 82*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 54*x^84 + 25*x^83 + 20*x^82 + 63*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 3*x^75 + 36*x^74 + 21*x^73 + 110*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 58*x^68 + 39*x^67 + 60*x^66 + 33*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 89*x^27 + 60*x^26 + 15*x^25 + 26*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 78*x^20 + 61*x^19 + 36*x^18 + 123*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 39*x^11 + 20*x^10 + 17*x^9 + 86*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 114*x^4 + 27*x^3 + 76*x^2 + 13*x + 118, x^95 + 15*x^93 + 74*x^92 + 69*x^91 + 116*x^90 + 3*x^89 + 14*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 106*x^84 + 57*x^83 + 44*x^82 + 31*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 35*x^75 + 28*x^74 + 117*x^73 + 50*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 38*x^68 + 7*x^67 + 4*x^66 + 65*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 57*x^27 + 4*x^26 + 47*x^25 + 70*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 82*x^20 + 93*x^19 + 28*x^18 + 91*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 71*x^11 + 44*x^10 + 113*x^9 + 74*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 110*x^4 + 123*x^3 + 116*x^2 + 45*x + 42, x^95 + 15*x^93 + 2*x^92 + 53*x^91 + 68*x^90 + 115*x^89 + 54*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 34*x^84 + 9*x^83 + 92*x^82 + 111*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 115*x^75 + 12*x^74 + 69*x^73 + 10*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 46*x^68 + 119*x^67 + 20*x^66 + 49*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 105*x^27 + 20*x^26 + 95*x^25 + 14*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 106*x^20 + 109*x^19 + 12*x^18 + 107*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 87*x^11 + 92*x^10 + x^9 + 66*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 86*x^4 + 43*x^3 + 68*x^2 + 93*x + 34, x^95 + 15*x^93 + 94*x^92 + 69*x^91 + 12*x^90 + 99*x^89 + 26*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 94*x^84 + 57*x^83 + 20*x^82 + 63*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 35*x^75 + 100*x^74 + 21*x^73 + 102*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 18*x^68 + 7*x^67 + 60*x^66 + 33*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 57*x^27 + 124*x^26 + 15*x^25 + 2*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 22*x^20 + 93*x^19 + 36*x^18 + 123*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 71*x^11 + 84*x^10 + 17*x^9 + 110*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 106*x^4 + 123*x^3 + 76*x^2 + 13*x + 46, x^95 + 15*x^93 + 86*x^92 + 53*x^91 + 92*x^90 + 83*x^89 + 66*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 86*x^84 + 9*x^83 + 68*x^82 + 15*x^81 + 114*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 115*x^75 + 84*x^74 + 101*x^73 + 62*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 90*x^68 + 119*x^67 + 76*x^66 + 17*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 105*x^27 + 12*x^26 + 63*x^25 + 74*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 110*x^20 + 109*x^19 + 20*x^18 + 11*x^17 + 122*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 87*x^11 + 4*x^10 + 33*x^9 + 102*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 18*x^4 + 43*x^3 + 28*x^2 + 61*x + 38, x^95 + 15*x^93 + 54*x^92 + 21*x^91 + 28*x^90 + 115*x^89 + 98*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 54*x^84 + 41*x^83 + 4*x^82 + 111*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 19*x^75 + 20*x^74 + 69*x^73 + 30*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 122*x^68 + 87*x^67 + 12*x^66 + 49*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 73*x^27 + 76*x^26 + 95*x^25 + 106*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 78*x^20 + 13*x^19 + 84*x^18 + 107*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 119*x^11 + 68*x^10 + x^9 + 70*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 50*x^4 + 11*x^3 + 92*x^2 + 93*x + 6, x^95 + 15*x^93 + 22*x^92 + 53*x^91 + 124*x^90 + 19*x^89 + 34*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 86*x^84 + 9*x^83 + 36*x^82 + 79*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 115*x^75 + 52*x^74 + 37*x^73 + 94*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 90*x^68 + 119*x^67 + 108*x^66 + 81*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 105*x^27 + 44*x^26 + 127*x^25 + 42*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 110*x^20 + 109*x^19 + 116*x^18 + 75*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 87*x^11 + 100*x^10 + 97*x^9 + 6*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 18*x^4 + 43*x^3 + 60*x^2 + 125*x + 6, x^95 + 15*x^93 + 62*x^92 + 37*x^91 + 76*x^90 + 3*x^89 + 58*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 62*x^84 + 89*x^83 + 84*x^82 + 31*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 67*x^75 + 36*x^74 + 117*x^73 + 70*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 50*x^68 + 103*x^67 + 124*x^66 + 65*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 25*x^27 + 60*x^26 + 47*x^25 + 34*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 118*x^20 + 125*x^19 + 100*x^18 + 91*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 103*x^11 + 20*x^10 + 113*x^9 + 78*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 10*x^4 + 91*x^3 + 12*x^2 + 45*x + 14, x^95 + 15*x^93 + 74*x^92 + 5*x^91 + 84*x^90 + 67*x^89 + 46*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 42*x^84 + 121*x^83 + 76*x^82 + 95*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 99*x^75 + 60*x^74 + 53*x^73 + 18*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 102*x^68 + 71*x^67 + 100*x^66 + x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 121*x^27 + 100*x^26 + 111*x^25 + 102*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 18*x^20 + 29*x^19 + 60*x^18 + 27*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 7*x^11 + 76*x^10 + 49*x^9 + 42*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 46*x^4 + 59*x^3 + 84*x^2 + 109*x + 74, x^95 + 15*x^93 + 10*x^92 + 53*x^91 + 68*x^90 + 83*x^89 + 126*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 74*x^84 + 9*x^83 + 28*x^82 + 15*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 115*x^75 + 12*x^74 + 101*x^73 + 2*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 6*x^68 + 119*x^67 + 84*x^66 + 17*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 105*x^27 + 20*x^26 + 63*x^25 + 118*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 50*x^20 + 109*x^19 + 76*x^18 + 11*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 87*x^11 + 92*x^10 + 33*x^9 + 90*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 78*x^4 + 43*x^3 + 4*x^2 + 61*x + 90, x^95 + 15*x^93 + 98*x^92 + 101*x^91 + 84*x^90 + 67*x^89 + 70*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 34*x^84 + 25*x^83 + 12*x^82 + 95*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 3*x^75 + 60*x^74 + 53*x^73 + 58*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 110*x^68 + 39*x^67 + 36*x^66 + x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 89*x^27 + 100*x^26 + 111*x^25 + 94*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 106*x^20 + 61*x^19 + 124*x^18 + 27*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 39*x^11 + 76*x^10 + 49*x^9 + 50*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 22*x^4 + 27*x^3 + 20*x^2 + 109*x + 50, x^95 + 15*x^93 + 50*x^92 + 85*x^91 + 4*x^90 + 19*x^89 + 38*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 18*x^84 + 105*x^83 + 28*x^82 + 79*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 83*x^75 + 76*x^74 + 37*x^73 + 26*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 62*x^68 + 23*x^67 + 84*x^66 + 81*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 9*x^27 + 84*x^26 + 127*x^25 + 62*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 26*x^20 + 77*x^19 + 76*x^18 + 75*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 55*x^11 + 28*x^10 + 97*x^9 + 18*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 38*x^4 + 75*x^3 + 4*x^2 + 125*x + 50, x^95 + 15*x^93 + 2*x^92 + 21*x^91 + 100*x^90 + 83*x^89 + 86*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 98*x^84 + 41*x^83 + 60*x^82 + 15*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 19*x^75 + 108*x^74 + 101*x^73 + 106*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 110*x^68 + 87*x^67 + 52*x^66 + 17*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 73*x^27 + 52*x^26 + 63*x^25 + 46*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 42*x^20 + 13*x^19 + 108*x^18 + 11*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 119*x^11 + 60*x^10 + 33*x^9 + 34*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 22*x^4 + 11*x^3 + 100*x^2 + 61*x + 66, x^95 + 15*x^93 + 18*x^92 + 117*x^91 + 36*x^90 + 115*x^89 + 102*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 50*x^84 + 73*x^83 + 124*x^82 + 111*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 51*x^75 + 44*x^74 + 69*x^73 + 90*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 30*x^68 + 55*x^67 + 116*x^66 + 49*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 41*x^27 + 116*x^26 + 95*x^25 + 126*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 58*x^20 + 45*x^19 + 44*x^18 + 107*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 23*x^11 + 124*x^10 + x^9 + 82*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 6*x^4 + 107*x^3 + 36*x^2 + 93*x + 50, x^95 + 15*x^93 + 90*x^92 + 5*x^91 + 20*x^90 + 67*x^89 + 62*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 122*x^84 + 121*x^83 + 12*x^82 + 95*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 99*x^75 + 124*x^74 + 53*x^73 + 2*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 22*x^68 + 71*x^67 + 36*x^66 + x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 121*x^27 + 36*x^26 + 111*x^25 + 54*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 34*x^20 + 29*x^19 + 124*x^18 + 27*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 7*x^11 + 12*x^10 + 49*x^9 + 90*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 30*x^4 + 59*x^3 + 20*x^2 + 109*x + 58, x^95 + 15*x^93 + 110*x^92 + 37*x^91 + 76*x^90 + 67*x^89 + 106*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 46*x^84 + 89*x^83 + 84*x^82 + 95*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 67*x^75 + 36*x^74 + 53*x^73 + 22*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 66*x^68 + 103*x^67 + 124*x^66 + x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 25*x^27 + 60*x^26 + 111*x^25 + 18*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 38*x^20 + 125*x^19 + 100*x^18 + 27*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 103*x^11 + 20*x^10 + 49*x^9 + 94*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 90*x^4 + 91*x^3 + 12*x^2 + 109*x + 94, x^95 + 15*x^93 + 50*x^92 + 101*x^91 + 116*x^90 + 3*x^89 + 118*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 114*x^84 + 25*x^83 + 108*x^82 + 31*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 3*x^75 + 28*x^74 + 117*x^73 + 10*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 30*x^68 + 39*x^67 + 68*x^66 + 65*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 89*x^27 + 4*x^26 + 47*x^25 + 78*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 122*x^20 + 61*x^19 + 92*x^18 + 91*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 39*x^11 + 44*x^10 + 113*x^9 + 66*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 6*x^4 + 27*x^3 + 52*x^2 + 45*x + 66, x^95 + 15*x^93 + 26*x^92 + 5*x^91 + 20*x^90 + 67*x^89 + 126*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 58*x^84 + 121*x^83 + 12*x^82 + 95*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 99*x^75 + 124*x^74 + 53*x^73 + 66*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 86*x^68 + 71*x^67 + 36*x^66 + x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 121*x^27 + 36*x^26 + 111*x^25 + 118*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 98*x^20 + 29*x^19 + 124*x^18 + 27*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 7*x^11 + 12*x^10 + 49*x^9 + 26*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 94*x^4 + 59*x^3 + 20*x^2 + 109*x + 122, x^95 + 15*x^93 + 118*x^92 + 53*x^91 + 60*x^90 + 19*x^89 + 66*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 54*x^84 + 9*x^83 + 100*x^82 + 79*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 115*x^75 + 116*x^74 + 37*x^73 + 62*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 122*x^68 + 119*x^67 + 44*x^66 + 81*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 105*x^27 + 108*x^26 + 127*x^25 + 74*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 78*x^20 + 109*x^19 + 52*x^18 + 75*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 87*x^11 + 36*x^10 + 97*x^9 + 102*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 50*x^4 + 43*x^3 + 124*x^2 + 125*x + 102, x^95 + 15*x^93 + 62*x^92 + 101*x^91 + 76*x^90 + 67*x^89 + 58*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 62*x^84 + 25*x^83 + 84*x^82 + 95*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 3*x^75 + 36*x^74 + 53*x^73 + 70*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 50*x^68 + 39*x^67 + 124*x^66 + x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 89*x^27 + 60*x^26 + 111*x^25 + 34*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 118*x^20 + 61*x^19 + 100*x^18 + 27*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 39*x^11 + 20*x^10 + 49*x^9 + 78*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 10*x^4 + 27*x^3 + 12*x^2 + 109*x + 14, x^95 + 15*x^93 + 106*x^92 + 21*x^91 + 68*x^90 + 51*x^89 + 30*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 42*x^84 + 41*x^83 + 28*x^82 + 47*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 19*x^75 + 12*x^74 + 5*x^73 + 98*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 38*x^68 + 87*x^67 + 84*x^66 + 113*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 73*x^27 + 20*x^26 + 31*x^25 + 22*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 18*x^20 + 13*x^19 + 76*x^18 + 43*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 119*x^11 + 92*x^10 + 65*x^9 + 58*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 110*x^4 + 11*x^3 + 4*x^2 + 29*x + 58, x^95 + 15*x^93 + 10*x^92 + 101*x^91 + 20*x^90 + 35*x^89 + 110*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 106*x^84 + 25*x^83 + 12*x^82 + 127*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 3*x^75 + 124*x^74 + 85*x^73 + 82*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 38*x^68 + 39*x^67 + 36*x^66 + 97*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 89*x^27 + 36*x^26 + 79*x^25 + 38*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 82*x^20 + 61*x^19 + 124*x^18 + 59*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 39*x^11 + 12*x^10 + 81*x^9 + 106*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 110*x^4 + 27*x^3 + 20*x^2 + 77*x + 10, x^95 + 15*x^93 + 62*x^92 + 53*x^91 + 124*x^90 + 115*x^89 + 74*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 30*x^84 + 9*x^83 + 100*x^82 + 111*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 115*x^75 + 52*x^74 + 69*x^73 + 118*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 18*x^68 + 119*x^67 + 44*x^66 + 49*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 105*x^27 + 44*x^26 + 95*x^25 + 114*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 86*x^20 + 109*x^19 + 52*x^18 + 107*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 87*x^11 + 100*x^10 + x^9 + 62*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 106*x^4 + 43*x^3 + 124*x^2 + 93*x + 94, x^95 + 15*x^93 + 18*x^92 + 5*x^91 + 116*x^90 + 35*x^89 + 22*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 82*x^84 + 121*x^83 + 108*x^82 + 127*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 99*x^75 + 28*x^74 + 85*x^73 + 106*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 62*x^68 + 71*x^67 + 68*x^66 + 97*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 121*x^27 + 4*x^26 + 79*x^25 + 110*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 90*x^20 + 29*x^19 + 92*x^18 + 59*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 7*x^11 + 44*x^10 + 81*x^9 + 34*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 38*x^4 + 59*x^3 + 52*x^2 + 77*x + 34, x^95 + 15*x^93 + 50*x^92 + 5*x^91 + 84*x^90 + 35*x^89 + 86*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 50*x^84 + 121*x^83 + 12*x^82 + 127*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 99*x^75 + 60*x^74 + 85*x^73 + 42*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 94*x^68 + 71*x^67 + 36*x^66 + 97*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 121*x^27 + 100*x^26 + 79*x^25 + 46*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 58*x^20 + 29*x^19 + 124*x^18 + 59*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 7*x^11 + 76*x^10 + 81*x^9 + 98*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 70*x^4 + 59*x^3 + 20*x^2 + 77*x + 34, x^95 + 15*x^93 + 54*x^92 + 37*x^91 + 76*x^90 + 35*x^89 + 50*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 22*x^84 + 89*x^83 + 20*x^82 + 127*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 67*x^75 + 36*x^74 + 85*x^73 + 14*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 90*x^68 + 103*x^67 + 60*x^66 + 97*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 25*x^27 + 60*x^26 + 79*x^25 + 122*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 46*x^20 + 125*x^19 + 36*x^18 + 59*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 103*x^11 + 20*x^10 + 81*x^9 + 118*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 18*x^4 + 91*x^3 + 76*x^2 + 77*x + 22, x^95 + 15*x^93 + 98*x^92 + 101*x^91 + 116*x^90 + 3*x^89 + 102*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 98*x^84 + 25*x^83 + 108*x^82 + 31*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 3*x^75 + 28*x^74 + 117*x^73 + 26*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 46*x^68 + 39*x^67 + 68*x^66 + 65*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 89*x^27 + 4*x^26 + 47*x^25 + 126*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 42*x^20 + 61*x^19 + 92*x^18 + 91*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 39*x^11 + 44*x^10 + 113*x^9 + 18*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 86*x^4 + 27*x^3 + 52*x^2 + 45*x + 82, x^95 + 15*x^93 + 62*x^92 + 69*x^91 + 44*x^90 + 35*x^89 + 26*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 126*x^84 + 57*x^83 + 116*x^82 + 127*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 35*x^75 + 68*x^74 + 85*x^73 + 102*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 114*x^68 + 7*x^67 + 92*x^66 + 97*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 57*x^27 + 28*x^26 + 79*x^25 + 2*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 54*x^20 + 93*x^19 + 4*x^18 + 59*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 71*x^11 + 52*x^10 + 81*x^9 + 110*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 74*x^4 + 123*x^3 + 108*x^2 + 77*x + 110, x^95 + 15*x^93 + 34*x^92 + 101*x^91 + 116*x^90 + 67*x^89 + 102*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 34*x^84 + 25*x^83 + 108*x^82 + 95*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 3*x^75 + 28*x^74 + 53*x^73 + 26*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 110*x^68 + 39*x^67 + 68*x^66 + x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 89*x^27 + 4*x^26 + 111*x^25 + 126*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 106*x^20 + 61*x^19 + 92*x^18 + 27*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 39*x^11 + 44*x^10 + 49*x^9 + 18*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 22*x^4 + 27*x^3 + 52*x^2 + 109*x + 82, x^95 + 15*x^93 + 122*x^92 + 117*x^91 + 36*x^90 + 19*x^89 + 78*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 58*x^84 + 73*x^83 + 60*x^82 + 79*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 51*x^75 + 44*x^74 + 37*x^73 + 50*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 22*x^68 + 55*x^67 + 52*x^66 + 81*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 41*x^27 + 116*x^26 + 127*x^25 + 6*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 98*x^20 + 45*x^19 + 108*x^18 + 75*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 23*x^11 + 124*x^10 + 97*x^9 + 74*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 30*x^4 + 107*x^3 + 100*x^2 + 125*x + 74, x^95 + 15*x^93 + 86*x^92 + 5*x^91 + 108*x^90 + 3*x^89 + 114*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 118*x^84 + 121*x^83 + 116*x^82 + 31*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 99*x^75 + 4*x^74 + 117*x^73 + 78*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 122*x^68 + 71*x^67 + 92*x^66 + 65*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 121*x^27 + 92*x^26 + 47*x^25 + 58*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 14*x^20 + 29*x^19 + 4*x^18 + 91*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 7*x^11 + 116*x^10 + 113*x^9 + 54*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 50*x^4 + 59*x^3 + 108*x^2 + 45*x + 22, x^95 + 15*x^93 + 54*x^92 + 117*x^91 + 92*x^90 + 19*x^89 + 34*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 54*x^84 + 73*x^83 + 68*x^82 + 79*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 51*x^75 + 84*x^74 + 37*x^73 + 94*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 122*x^68 + 55*x^67 + 76*x^66 + 81*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 41*x^27 + 12*x^26 + 127*x^25 + 42*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 78*x^20 + 45*x^19 + 20*x^18 + 75*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 23*x^11 + 4*x^10 + 97*x^9 + 6*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 50*x^4 + 107*x^3 + 28*x^2 + 125*x + 70, x^95 + 15*x^93 + 26*x^92 + 85*x^91 + 4*x^90 + 115*x^89 + 78*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 26*x^84 + 105*x^83 + 92*x^82 + 111*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 83*x^75 + 76*x^74 + 69*x^73 + 50*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 54*x^68 + 23*x^67 + 20*x^66 + 49*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 9*x^27 + 84*x^26 + 95*x^25 + 6*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 66*x^20 + 77*x^19 + 12*x^18 + 107*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 55*x^11 + 28*x^10 + x^9 + 74*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 62*x^4 + 75*x^3 + 68*x^2 + 93*x + 10, x^95 + 15*x^93 + 98*x^92 + 5*x^91 + 20*x^90 + 35*x^89 + 6*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 34*x^84 + 121*x^83 + 76*x^82 + 127*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 99*x^75 + 124*x^74 + 85*x^73 + 122*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 110*x^68 + 71*x^67 + 100*x^66 + 97*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 121*x^27 + 36*x^26 + 79*x^25 + 30*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 106*x^20 + 29*x^19 + 60*x^18 + 59*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 7*x^11 + 12*x^10 + 81*x^9 + 114*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 22*x^4 + 59*x^3 + 84*x^2 + 77*x + 114, x^95 + 15*x^93 + 122*x^92 + 53*x^91 + 36*x^90 + 83*x^89 + 78*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 58*x^84 + 9*x^83 + 60*x^82 + 15*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 115*x^75 + 44*x^74 + 101*x^73 + 50*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 22*x^68 + 119*x^67 + 52*x^66 + 17*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 105*x^27 + 116*x^26 + 63*x^25 + 6*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 98*x^20 + 109*x^19 + 108*x^18 + 11*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 87*x^11 + 124*x^10 + 33*x^9 + 74*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 30*x^4 + 43*x^3 + 100*x^2 + 61*x + 74, x^95 + 15*x^93 + 122*x^92 + 37*x^91 + 52*x^90 + 35*x^89 + 62*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 90*x^84 + 89*x^83 + 108*x^82 + 127*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 67*x^75 + 92*x^74 + 85*x^73 + 2*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 54*x^68 + 103*x^67 + 68*x^66 + 97*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 25*x^27 + 68*x^26 + 79*x^25 + 54*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 2*x^20 + 125*x^19 + 92*x^18 + 59*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 103*x^11 + 108*x^10 + 81*x^9 + 90*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 62*x^4 + 91*x^3 + 52*x^2 + 77*x + 122, x^95 + 15*x^93 + 58*x^92 + 5*x^91 + 116*x^90 + 3*x^89 + 126*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 26*x^84 + 121*x^83 + 44*x^82 + 31*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 99*x^75 + 28*x^74 + 117*x^73 + 66*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 118*x^68 + 71*x^67 + 4*x^66 + 65*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 121*x^27 + 4*x^26 + 47*x^25 + 118*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 66*x^20 + 29*x^19 + 28*x^18 + 91*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 7*x^11 + 44*x^10 + 113*x^9 + 26*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 126*x^4 + 59*x^3 + 116*x^2 + 45*x + 58, x^95 + 15*x^93 + 78*x^92 + 37*x^91 + 76*x^90 + 3*x^89 + 10*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 14*x^84 + 89*x^83 + 84*x^82 + 31*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 67*x^75 + 36*x^74 + 117*x^73 + 118*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 98*x^68 + 103*x^67 + 124*x^66 + 65*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 25*x^27 + 60*x^26 + 47*x^25 + 50*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 6*x^20 + 125*x^19 + 100*x^18 + 91*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 103*x^11 + 20*x^10 + 113*x^9 + 62*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 122*x^4 + 91*x^3 + 12*x^2 + 45*x + 62, x^95 + 15*x^93 + 126*x^92 + 85*x^91 + 28*x^90 + 83*x^89 + 106*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 30*x^84 + 105*x^83 + 68*x^82 + 15*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 83*x^75 + 20*x^74 + 101*x^73 + 86*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 18*x^68 + 23*x^67 + 76*x^66 + 17*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 9*x^27 + 76*x^26 + 63*x^25 + 18*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 86*x^20 + 77*x^19 + 20*x^18 + 11*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 55*x^11 + 68*x^10 + 33*x^9 + 30*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 106*x^4 + 75*x^3 + 28*x^2 + 61*x + 126, x^95 + 15*x^93 + 102*x^92 + 21*x^91 + 124*x^90 + 115*x^89 + 114*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 102*x^84 + 41*x^83 + 36*x^82 + 111*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 19*x^75 + 52*x^74 + 69*x^73 + 14*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 74*x^68 + 87*x^67 + 108*x^66 + 49*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 73*x^27 + 44*x^26 + 95*x^25 + 58*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 62*x^20 + 13*x^19 + 116*x^18 + 107*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 119*x^11 + 100*x^10 + x^9 + 118*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 66*x^4 + 11*x^3 + 60*x^2 + 93*x + 54, x^95 + 15*x^93 + 2*x^92 + 21*x^91 + 68*x^90 + 19*x^89 + 54*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 34*x^84 + 41*x^83 + 92*x^82 + 79*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 19*x^75 + 12*x^74 + 37*x^73 + 10*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 46*x^68 + 87*x^67 + 20*x^66 + 81*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 73*x^27 + 20*x^26 + 127*x^25 + 14*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 106*x^20 + 13*x^19 + 12*x^18 + 75*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 119*x^11 + 92*x^10 + 97*x^9 + 66*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 86*x^4 + 11*x^3 + 68*x^2 + 125*x + 34, x^95 + 15*x^93 + 2*x^92 + 117*x^91 + 68*x^90 + 115*x^89 + 118*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 34*x^84 + 73*x^83 + 92*x^82 + 111*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 51*x^75 + 12*x^74 + 69*x^73 + 74*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 46*x^68 + 55*x^67 + 20*x^66 + 49*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 41*x^27 + 20*x^26 + 95*x^25 + 78*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 106*x^20 + 45*x^19 + 12*x^18 + 107*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 23*x^11 + 92*x^10 + x^9 + 2*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 86*x^4 + 107*x^3 + 68*x^2 + 93*x + 98, x^95 + 15*x^93 + 74*x^92 + 53*x^91 + 100*x^90 + 83*x^89 + 30*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 74*x^84 + 9*x^83 + 124*x^82 + 15*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 115*x^75 + 108*x^74 + 101*x^73 + 98*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 6*x^68 + 119*x^67 + 116*x^66 + 17*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 105*x^27 + 52*x^26 + 63*x^25 + 22*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 50*x^20 + 109*x^19 + 44*x^18 + 11*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 87*x^11 + 60*x^10 + 33*x^9 + 58*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 78*x^4 + 43*x^3 + 36*x^2 + 61*x + 122, x^95 + 15*x^93 + 14*x^92 + 117*x^91 + 92*x^90 + 51*x^89 + 122*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 110*x^84 + 73*x^83 + 4*x^82 + 47*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 51*x^75 + 84*x^74 + 5*x^73 + 70*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 66*x^68 + 55*x^67 + 12*x^66 + 113*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 41*x^27 + 12*x^26 + 31*x^25 + 98*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 102*x^20 + 45*x^19 + 84*x^18 + 43*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 23*x^11 + 4*x^10 + 65*x^9 + 78*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 90*x^4 + 107*x^3 + 92*x^2 + 29*x + 110, x^95 + 15*x^93 + 94*x^92 + 37*x^91 + 108*x^90 + 3*x^89 + 58*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 30*x^84 + 89*x^83 + 52*x^82 + 31*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 67*x^75 + 4*x^74 + 117*x^73 + 70*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 82*x^68 + 103*x^67 + 28*x^66 + 65*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 25*x^27 + 92*x^26 + 47*x^25 + 34*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 86*x^20 + 125*x^19 + 68*x^18 + 91*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 103*x^11 + 116*x^10 + 113*x^9 + 78*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 42*x^4 + 91*x^3 + 44*x^2 + 45*x + 78, x^95 + 15*x^93 + 62*x^92 + 85*x^91 + 60*x^90 + 19*x^89 + 74*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 30*x^84 + 105*x^83 + 36*x^82 + 79*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 83*x^75 + 116*x^74 + 37*x^73 + 118*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 18*x^68 + 23*x^67 + 108*x^66 + 81*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 9*x^27 + 108*x^26 + 127*x^25 + 114*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 86*x^20 + 77*x^19 + 116*x^18 + 75*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 55*x^11 + 36*x^10 + 97*x^9 + 62*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 106*x^4 + 75*x^3 + 60*x^2 + 125*x + 94, x^95 + 15*x^93 + 102*x^92 + 101*x^91 + 12*x^90 + 99*x^89 + 98*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 6*x^84 + 25*x^83 + 84*x^82 + 63*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 3*x^75 + 100*x^74 + 21*x^73 + 94*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 106*x^68 + 39*x^67 + 124*x^66 + 33*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 89*x^27 + 124*x^26 + 15*x^25 + 106*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 94*x^20 + 61*x^19 + 100*x^18 + 123*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 39*x^11 + 84*x^10 + 17*x^9 + 6*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 98*x^4 + 27*x^3 + 12*x^2 + 13*x + 102, x^95 + 15*x^93 + 66*x^92 + 37*x^91 + 20*x^90 + 67*x^89 + 38*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 2*x^84 + 89*x^83 + 76*x^82 + 95*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 67*x^75 + 124*x^74 + 53*x^73 + 90*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 14*x^68 + 103*x^67 + 100*x^66 + x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 25*x^27 + 36*x^26 + 111*x^25 + 62*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 74*x^20 + 125*x^19 + 60*x^18 + 27*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 103*x^11 + 12*x^10 + 49*x^9 + 82*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 54*x^4 + 91*x^3 + 84*x^2 + 109*x + 82, x^95 + 15*x^93 + 30*x^92 + 85*x^91 + 124*x^90 + 19*x^89 + 106*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 126*x^84 + 105*x^83 + 100*x^82 + 79*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 83*x^75 + 52*x^74 + 37*x^73 + 86*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 50*x^68 + 23*x^67 + 44*x^66 + 81*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 9*x^27 + 44*x^26 + 127*x^25 + 18*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 54*x^20 + 77*x^19 + 52*x^18 + 75*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 55*x^11 + 100*x^10 + 97*x^9 + 30*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 10*x^4 + 75*x^3 + 124*x^2 + 125*x + 62, x^95 + 15*x^93 + 110*x^92 + 101*x^91 + 108*x^90 + 3*x^89 + 74*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 110*x^84 + 25*x^83 + 52*x^82 + 31*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 3*x^75 + 4*x^74 + 117*x^73 + 54*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 2*x^68 + 39*x^67 + 28*x^66 + 65*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 89*x^27 + 92*x^26 + 47*x^25 + 114*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 102*x^20 + 61*x^19 + 68*x^18 + 91*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 39*x^11 + 116*x^10 + 113*x^9 + 126*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 26*x^4 + 27*x^3 + 44*x^2 + 45*x + 62, x^95 + 15*x^93 + 106*x^92 + 85*x^91 + 4*x^90 + 51*x^89 + 30*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 42*x^84 + 105*x^83 + 92*x^82 + 47*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 83*x^75 + 76*x^74 + 5*x^73 + 98*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 38*x^68 + 23*x^67 + 20*x^66 + 113*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 9*x^27 + 84*x^26 + 31*x^25 + 22*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 18*x^20 + 77*x^19 + 12*x^18 + 43*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 55*x^11 + 28*x^10 + 65*x^9 + 58*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 110*x^4 + 75*x^3 + 68*x^2 + 29*x + 58, x^95 + 15*x^93 + 82*x^92 + 69*x^91 + 116*x^90 + 99*x^89 + 86*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 18*x^84 + 57*x^83 + 108*x^82 + 63*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 35*x^75 + 28*x^74 + 21*x^73 + 42*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 126*x^68 + 7*x^67 + 68*x^66 + 33*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 57*x^27 + 4*x^26 + 15*x^25 + 46*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 26*x^20 + 93*x^19 + 92*x^18 + 123*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 71*x^11 + 44*x^10 + 17*x^9 + 98*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 102*x^4 + 123*x^3 + 52*x^2 + 13*x + 98, x^95 + 15*x^93 + 126*x^92 + 21*x^91 + 28*x^90 + 19*x^89 + 106*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 30*x^84 + 41*x^83 + 68*x^82 + 79*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 19*x^75 + 20*x^74 + 37*x^73 + 86*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 18*x^68 + 87*x^67 + 76*x^66 + 81*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 73*x^27 + 76*x^26 + 127*x^25 + 18*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 86*x^20 + 13*x^19 + 20*x^18 + 75*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 119*x^11 + 68*x^10 + 97*x^9 + 30*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 106*x^4 + 11*x^3 + 28*x^2 + 125*x + 126, x^95 + 15*x^93 + 58*x^92 + 69*x^91 + 116*x^90 + 3*x^89 + 62*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 26*x^84 + 57*x^83 + 44*x^82 + 31*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 35*x^75 + 28*x^74 + 117*x^73 + 2*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 118*x^68 + 7*x^67 + 4*x^66 + 65*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 57*x^27 + 4*x^26 + 47*x^25 + 54*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 66*x^20 + 93*x^19 + 28*x^18 + 91*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 71*x^11 + 44*x^10 + 113*x^9 + 90*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 126*x^4 + 123*x^3 + 116*x^2 + 45*x + 122, x^95 + 15*x^93 + 62*x^92 + 21*x^91 + 28*x^90 + 19*x^89 + 42*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 94*x^84 + 41*x^83 + 68*x^82 + 79*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 19*x^75 + 20*x^74 + 37*x^73 + 22*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 82*x^68 + 87*x^67 + 76*x^66 + 81*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 73*x^27 + 76*x^26 + 127*x^25 + 82*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 22*x^20 + 13*x^19 + 20*x^18 + 75*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 119*x^11 + 68*x^10 + 97*x^9 + 94*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 42*x^4 + 11*x^3 + 28*x^2 + 125*x + 62, x^95 + 15*x^93 + 114*x^92 + 69*x^91 + 84*x^90 + 35*x^89 + 86*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 114*x^84 + 57*x^83 + 12*x^82 + 127*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 35*x^75 + 60*x^74 + 85*x^73 + 42*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 30*x^68 + 7*x^67 + 36*x^66 + 97*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 57*x^27 + 100*x^26 + 79*x^25 + 46*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 122*x^20 + 93*x^19 + 124*x^18 + 59*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 71*x^11 + 76*x^10 + 81*x^9 + 98*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 6*x^4 + 123*x^3 + 20*x^2 + 77*x + 34, x^95 + 15*x^93 + 6*x^92 + 85*x^91 + 60*x^90 + 51*x^89 + 82*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 6*x^84 + 105*x^83 + 100*x^82 + 47*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 83*x^75 + 116*x^74 + 5*x^73 + 46*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 42*x^68 + 23*x^67 + 44*x^66 + 113*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 9*x^27 + 108*x^26 + 31*x^25 + 26*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 94*x^20 + 77*x^19 + 52*x^18 + 43*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 55*x^11 + 36*x^10 + 65*x^9 + 22*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 34*x^4 + 75*x^3 + 124*x^2 + 29*x + 86, x^95 + 15*x^93 + 66*x^92 + 69*x^91 + 84*x^90 + 35*x^89 + 102*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 2*x^84 + 57*x^83 + 12*x^82 + 127*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 35*x^75 + 60*x^74 + 85*x^73 + 26*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 14*x^68 + 7*x^67 + 36*x^66 + 97*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 57*x^27 + 100*x^26 + 79*x^25 + 126*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 74*x^20 + 93*x^19 + 124*x^18 + 59*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 71*x^11 + 76*x^10 + 81*x^9 + 18*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 54*x^4 + 123*x^3 + 20*x^2 + 77*x + 18, x^95 + 15*x^93 + 90*x^92 + 69*x^91 + 20*x^90 + 67*x^89 + 126*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 122*x^84 + 57*x^83 + 12*x^82 + 95*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 35*x^75 + 124*x^74 + 53*x^73 + 66*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 22*x^68 + 7*x^67 + 36*x^66 + x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 57*x^27 + 36*x^26 + 111*x^25 + 118*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 34*x^20 + 93*x^19 + 124*x^18 + 27*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 71*x^11 + 12*x^10 + 49*x^9 + 26*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 30*x^4 + 123*x^3 + 20*x^2 + 109*x + 122, x^95 + 15*x^93 + 42*x^92 + 5*x^91 + 52*x^90 + 67*x^89 + 46*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 74*x^84 + 121*x^83 + 108*x^82 + 95*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 99*x^75 + 92*x^74 + 53*x^73 + 18*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 70*x^68 + 71*x^67 + 68*x^66 + x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 121*x^27 + 68*x^26 + 111*x^25 + 102*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 50*x^20 + 29*x^19 + 92*x^18 + 27*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 7*x^11 + 108*x^10 + 49*x^9 + 42*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 14*x^4 + 59*x^3 + 52*x^2 + 109*x + 10, x^95 + 15*x^93 + 86*x^92 + 69*x^91 + 76*x^90 + 3*x^89 + 82*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 54*x^84 + 57*x^83 + 20*x^82 + 31*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 35*x^75 + 36*x^74 + 117*x^73 + 110*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 58*x^68 + 7*x^67 + 60*x^66 + 65*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 57*x^27 + 60*x^26 + 47*x^25 + 26*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 78*x^20 + 93*x^19 + 36*x^18 + 91*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 71*x^11 + 20*x^10 + 113*x^9 + 86*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 114*x^4 + 123*x^3 + 76*x^2 + 45*x + 118, x^95 + 15*x^93 + 110*x^92 + 85*x^91 + 28*x^90 + 19*x^89 + 90*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 78*x^84 + 105*x^83 + 68*x^82 + 79*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 83*x^75 + 20*x^74 + 37*x^73 + 102*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 98*x^68 + 23*x^67 + 76*x^66 + 81*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 9*x^27 + 76*x^26 + 127*x^25 + 66*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 70*x^20 + 77*x^19 + 20*x^18 + 75*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 55*x^11 + 68*x^10 + 97*x^9 + 110*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 122*x^4 + 75*x^3 + 28*x^2 + 125*x + 14, x^95 + 15*x^93 + 86*x^92 + 69*x^91 + 108*x^90 + 67*x^89 + 114*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 118*x^84 + 57*x^83 + 116*x^82 + 95*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 35*x^75 + 4*x^74 + 53*x^73 + 78*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 122*x^68 + 7*x^67 + 92*x^66 + x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 57*x^27 + 92*x^26 + 111*x^25 + 58*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 14*x^20 + 93*x^19 + 4*x^18 + 27*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 71*x^11 + 116*x^10 + 49*x^9 + 54*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 50*x^4 + 123*x^3 + 108*x^2 + 109*x + 22, x^95 + 15*x^93 + 110*x^92 + 53*x^91 + 28*x^90 + 51*x^89 + 90*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 78*x^84 + 9*x^83 + 68*x^82 + 47*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 115*x^75 + 20*x^74 + 5*x^73 + 102*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 98*x^68 + 119*x^67 + 76*x^66 + 113*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 105*x^27 + 76*x^26 + 31*x^25 + 66*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 70*x^20 + 109*x^19 + 20*x^18 + 43*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 87*x^11 + 68*x^10 + 65*x^9 + 110*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 122*x^4 + 43*x^3 + 28*x^2 + 29*x + 14, x^95 + 15*x^93 + 18*x^92 + 117*x^91 + 36*x^90 + 51*x^89 + 38*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 50*x^84 + 73*x^83 + 124*x^82 + 47*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 51*x^75 + 44*x^74 + 5*x^73 + 26*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 30*x^68 + 55*x^67 + 116*x^66 + 113*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 41*x^27 + 116*x^26 + 31*x^25 + 62*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 58*x^20 + 45*x^19 + 44*x^18 + 43*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 23*x^11 + 124*x^10 + 65*x^9 + 18*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 6*x^4 + 107*x^3 + 36*x^2 + 29*x + 114, x^95 + 15*x^93 + 46*x^92 + 21*x^91 + 60*x^90 + 83*x^89 + 122*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 78*x^84 + 41*x^83 + 36*x^82 + 15*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 19*x^75 + 116*x^74 + 101*x^73 + 70*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 98*x^68 + 87*x^67 + 108*x^66 + 17*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 73*x^27 + 108*x^26 + 63*x^25 + 98*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 70*x^20 + 13*x^19 + 116*x^18 + 11*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 119*x^11 + 36*x^10 + 33*x^9 + 78*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 122*x^4 + 11*x^3 + 60*x^2 + 61*x + 46, x^95 + 15*x^93 + 66*x^92 + 37*x^91 + 84*x^90 + 3*x^89 + 38*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 2*x^84 + 89*x^83 + 12*x^82 + 31*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 67*x^75 + 60*x^74 + 117*x^73 + 90*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 14*x^68 + 103*x^67 + 36*x^66 + 65*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 25*x^27 + 100*x^26 + 47*x^25 + 62*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 74*x^20 + 125*x^19 + 124*x^18 + 91*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 103*x^11 + 76*x^10 + 113*x^9 + 82*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 54*x^4 + 91*x^3 + 20*x^2 + 45*x + 82, x^95 + 15*x^93 + 38*x^92 + 5*x^91 + 76*x^90 + 67*x^89 + 98*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 70*x^84 + 121*x^83 + 20*x^82 + 95*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 99*x^75 + 36*x^74 + 53*x^73 + 94*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 42*x^68 + 71*x^67 + 60*x^66 + x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 121*x^27 + 60*x^26 + 111*x^25 + 106*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 30*x^20 + 29*x^19 + 36*x^18 + 27*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 7*x^11 + 20*x^10 + 49*x^9 + 6*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 34*x^4 + 59*x^3 + 76*x^2 + 109*x + 102, x^95 + 15*x^93 + 102*x^92 + 53*x^91 + 92*x^90 + 19*x^89 + 82*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 38*x^84 + 9*x^83 + 68*x^82 + 79*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 115*x^75 + 84*x^74 + 37*x^73 + 46*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 10*x^68 + 119*x^67 + 76*x^66 + 81*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 105*x^27 + 12*x^26 + 127*x^25 + 26*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 126*x^20 + 109*x^19 + 20*x^18 + 75*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 87*x^11 + 4*x^10 + 97*x^9 + 22*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 2*x^4 + 43*x^3 + 28*x^2 + 125*x + 22, x^95 + 15*x^93 + 106*x^92 + 69*x^91 + 52*x^90 + 67*x^89 + 46*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 10*x^84 + 57*x^83 + 108*x^82 + 95*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 35*x^75 + 92*x^74 + 53*x^73 + 18*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 6*x^68 + 7*x^67 + 68*x^66 + x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 57*x^27 + 68*x^26 + 111*x^25 + 102*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 114*x^20 + 93*x^19 + 92*x^18 + 27*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 71*x^11 + 108*x^10 + 49*x^9 + 42*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 78*x^4 + 123*x^3 + 52*x^2 + 109*x + 10, x^95 + 15*x^93 + 14*x^92 + 5*x^91 + 76*x^90 + 99*x^89 + 10*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 78*x^84 + 121*x^83 + 84*x^82 + 63*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 99*x^75 + 36*x^74 + 21*x^73 + 118*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 34*x^68 + 71*x^67 + 124*x^66 + 33*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 121*x^27 + 60*x^26 + 15*x^25 + 50*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 70*x^20 + 29*x^19 + 100*x^18 + 123*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 7*x^11 + 20*x^10 + 17*x^9 + 62*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 58*x^4 + 59*x^3 + 12*x^2 + 13*x + 62, x^95 + 15*x^93 + 114*x^92 + 37*x^91 + 52*x^90 + 67*x^89 + 118*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 50*x^84 + 89*x^83 + 44*x^82 + 95*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 67*x^75 + 92*x^74 + 53*x^73 + 10*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 94*x^68 + 103*x^67 + 4*x^66 + x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 25*x^27 + 68*x^26 + 111*x^25 + 78*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 58*x^20 + 125*x^19 + 28*x^18 + 27*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 103*x^11 + 108*x^10 + 49*x^9 + 66*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 70*x^4 + 91*x^3 + 116*x^2 + 109*x + 66, x^95 + 15*x^93 + 14*x^92 + 85*x^91 + 60*x^90 + 83*x^89 + 26*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 46*x^84 + 105*x^83 + 36*x^82 + 15*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 83*x^75 + 116*x^74 + 101*x^73 + 38*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 2*x^68 + 23*x^67 + 108*x^66 + 17*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 9*x^27 + 108*x^26 + 63*x^25 + 2*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 38*x^20 + 77*x^19 + 116*x^18 + 11*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 55*x^11 + 36*x^10 + 33*x^9 + 46*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 26*x^4 + 75*x^3 + 60*x^2 + 61*x + 14, x^95 + 15*x^93 + 70*x^92 + 69*x^91 + 108*x^90 + 3*x^89 + 98*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 38*x^84 + 57*x^83 + 116*x^82 + 31*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 35*x^75 + 4*x^74 + 117*x^73 + 94*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 74*x^68 + 7*x^67 + 92*x^66 + 65*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 57*x^27 + 92*x^26 + 47*x^25 + 106*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 126*x^20 + 93*x^19 + 4*x^18 + 91*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 71*x^11 + 116*x^10 + 113*x^9 + 6*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 66*x^4 + 123*x^3 + 108*x^2 + 45*x + 38, x^95 + 15*x^93 + 14*x^92 + 5*x^91 + 108*x^90 + 35*x^89 + 42*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 14*x^84 + 121*x^83 + 52*x^82 + 127*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 99*x^75 + 4*x^74 + 85*x^73 + 86*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 98*x^68 + 71*x^67 + 28*x^66 + 97*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 121*x^27 + 92*x^26 + 79*x^25 + 82*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 6*x^20 + 29*x^19 + 68*x^18 + 59*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 7*x^11 + 116*x^10 + 81*x^9 + 30*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 122*x^4 + 59*x^3 + 44*x^2 + 77*x + 94, x^95 + 15*x^93 + 106*x^92 + 21*x^91 + 100*x^90 + 115*x^89 + 62*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 106*x^84 + 41*x^83 + 124*x^82 + 111*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 19*x^75 + 108*x^74 + 69*x^73 + 66*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 102*x^68 + 87*x^67 + 116*x^66 + 49*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 73*x^27 + 52*x^26 + 95*x^25 + 54*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 82*x^20 + 13*x^19 + 44*x^18 + 107*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 119*x^11 + 60*x^10 + x^9 + 26*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 46*x^4 + 11*x^3 + 36*x^2 + 93*x + 90, x^95 + 15*x^93 + 66*x^92 + 101*x^91 + 84*x^90 + 67*x^89 + 38*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 2*x^84 + 25*x^83 + 12*x^82 + 95*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 3*x^75 + 60*x^74 + 53*x^73 + 90*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 14*x^68 + 39*x^67 + 36*x^66 + x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 89*x^27 + 100*x^26 + 111*x^25 + 62*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 74*x^20 + 61*x^19 + 124*x^18 + 27*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 39*x^11 + 76*x^10 + 49*x^9 + 82*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 54*x^4 + 27*x^3 + 20*x^2 + 109*x + 82, x^95 + 15*x^93 + 114*x^92 + 5*x^91 + 52*x^90 + 99*x^89 + 118*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 50*x^84 + 121*x^83 + 44*x^82 + 63*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 99*x^75 + 92*x^74 + 21*x^73 + 10*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 94*x^68 + 71*x^67 + 4*x^66 + 33*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 121*x^27 + 68*x^26 + 15*x^25 + 78*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 58*x^20 + 29*x^19 + 28*x^18 + 123*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 7*x^11 + 108*x^10 + 17*x^9 + 66*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 70*x^4 + 59*x^3 + 116*x^2 + 13*x + 66, x^95 + 15*x^93 + 102*x^92 + 37*x^91 + 12*x^90 + 35*x^89 + 98*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 6*x^84 + 89*x^83 + 84*x^82 + 127*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 67*x^75 + 100*x^74 + 85*x^73 + 94*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 106*x^68 + 103*x^67 + 124*x^66 + 97*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 25*x^27 + 124*x^26 + 79*x^25 + 106*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 94*x^20 + 125*x^19 + 100*x^18 + 59*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 103*x^11 + 84*x^10 + 81*x^9 + 6*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 98*x^4 + 91*x^3 + 12*x^2 + 77*x + 102, x^95 + 15*x^93 + 114*x^92 + 117*x^91 + 68*x^90 + 115*x^89 + 38*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 82*x^84 + 73*x^83 + 92*x^82 + 111*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 51*x^75 + 12*x^74 + 69*x^73 + 26*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 126*x^68 + 55*x^67 + 20*x^66 + 49*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 41*x^27 + 20*x^26 + 95*x^25 + 62*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 90*x^20 + 45*x^19 + 12*x^18 + 107*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 23*x^11 + 92*x^10 + x^9 + 18*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 102*x^4 + 107*x^3 + 68*x^2 + 93*x + 50, x^95 + 15*x^93 + 34*x^92 + 85*x^91 + 68*x^90 + 19*x^89 + 22*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 66*x^84 + 105*x^83 + 92*x^82 + 79*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 83*x^75 + 12*x^74 + 37*x^73 + 42*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 14*x^68 + 23*x^67 + 20*x^66 + 81*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 9*x^27 + 20*x^26 + 127*x^25 + 110*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 10*x^20 + 77*x^19 + 12*x^18 + 75*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 55*x^11 + 92*x^10 + 97*x^9 + 98*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 54*x^4 + 75*x^3 + 68*x^2 + 125*x + 66, x^95 + 15*x^93 + 74*x^92 + 117*x^91 + 68*x^90 + 83*x^89 + 126*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 10*x^84 + 73*x^83 + 28*x^82 + 15*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 51*x^75 + 12*x^74 + 101*x^73 + 2*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 70*x^68 + 55*x^67 + 84*x^66 + 17*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 41*x^27 + 20*x^26 + 63*x^25 + 118*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 114*x^20 + 45*x^19 + 76*x^18 + 11*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 23*x^11 + 92*x^10 + 33*x^9 + 90*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 14*x^4 + 107*x^3 + 4*x^2 + 61*x + 90, x^95 + 15*x^93 + 30*x^92 + 85*x^91 + 60*x^90 + 83*x^89 + 106*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 126*x^84 + 105*x^83 + 36*x^82 + 15*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 83*x^75 + 116*x^74 + 101*x^73 + 86*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 50*x^68 + 23*x^67 + 108*x^66 + 17*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 9*x^27 + 108*x^26 + 63*x^25 + 18*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 54*x^20 + 77*x^19 + 116*x^18 + 11*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 55*x^11 + 36*x^10 + 33*x^9 + 30*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 10*x^4 + 75*x^3 + 60*x^2 + 61*x + 62, x^95 + 15*x^93 + 74*x^92 + 69*x^91 + 84*x^90 + 3*x^89 + 46*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 42*x^84 + 57*x^83 + 76*x^82 + 31*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 35*x^75 + 60*x^74 + 117*x^73 + 18*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 102*x^68 + 7*x^67 + 100*x^66 + 65*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 57*x^27 + 100*x^26 + 47*x^25 + 102*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 18*x^20 + 93*x^19 + 60*x^18 + 91*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 71*x^11 + 76*x^10 + 113*x^9 + 42*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 46*x^4 + 123*x^3 + 84*x^2 + 45*x + 74, x^95 + 15*x^93 + 110*x^92 + 53*x^91 + 124*x^90 + 51*x^89 + 122*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 14*x^84 + 9*x^83 + 100*x^82 + 47*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 115*x^75 + 52*x^74 + 5*x^73 + 70*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 34*x^68 + 119*x^67 + 44*x^66 + 113*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 105*x^27 + 44*x^26 + 31*x^25 + 98*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 6*x^20 + 109*x^19 + 52*x^18 + 43*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 87*x^11 + 100*x^10 + 65*x^9 + 78*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 58*x^4 + 43*x^3 + 124*x^2 + 29*x + 46, x^95 + 15*x^93 + 22*x^92 + 21*x^91 + 124*x^90 + 51*x^89 + 34*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 86*x^84 + 41*x^83 + 36*x^82 + 47*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 19*x^75 + 52*x^74 + 5*x^73 + 94*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 90*x^68 + 87*x^67 + 108*x^66 + 113*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 73*x^27 + 44*x^26 + 31*x^25 + 42*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 110*x^20 + 13*x^19 + 116*x^18 + 43*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 119*x^11 + 100*x^10 + 65*x^9 + 6*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 18*x^4 + 11*x^3 + 60*x^2 + 29*x + 6, x^95 + 15*x^93 + 2*x^92 + 37*x^91 + 84*x^90 + 67*x^89 + 38*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 66*x^84 + 89*x^83 + 12*x^82 + 95*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 67*x^75 + 60*x^74 + 53*x^73 + 90*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 78*x^68 + 103*x^67 + 36*x^66 + x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 25*x^27 + 100*x^26 + 111*x^25 + 62*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 10*x^20 + 125*x^19 + 124*x^18 + 27*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 103*x^11 + 76*x^10 + 49*x^9 + 82*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 118*x^4 + 91*x^3 + 20*x^2 + 109*x + 82, x^95 + 15*x^93 + 34*x^92 + 101*x^91 + 52*x^90 + 3*x^89 + 102*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 34*x^84 + 25*x^83 + 44*x^82 + 31*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 3*x^75 + 92*x^74 + 117*x^73 + 26*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 110*x^68 + 39*x^67 + 4*x^66 + 65*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 89*x^27 + 68*x^26 + 47*x^25 + 126*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 106*x^20 + 61*x^19 + 28*x^18 + 91*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 39*x^11 + 108*x^10 + 113*x^9 + 18*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 22*x^4 + 27*x^3 + 116*x^2 + 45*x + 82, x^95 + 15*x^93 + 126*x^92 + 53*x^91 + 60*x^90 + 115*x^89 + 74*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 94*x^84 + 9*x^83 + 36*x^82 + 111*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 115*x^75 + 116*x^74 + 69*x^73 + 118*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 82*x^68 + 119*x^67 + 108*x^66 + 49*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 105*x^27 + 108*x^26 + 95*x^25 + 114*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 22*x^20 + 109*x^19 + 116*x^18 + 107*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 87*x^11 + 36*x^10 + x^9 + 62*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 42*x^4 + 43*x^3 + 60*x^2 + 93*x + 94, x^95 + 15*x^93 + 50*x^92 + 101*x^91 + 20*x^90 + 67*x^89 + 22*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 50*x^84 + 25*x^83 + 76*x^82 + 95*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 3*x^75 + 124*x^74 + 53*x^73 + 106*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 94*x^68 + 39*x^67 + 100*x^66 + x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 89*x^27 + 36*x^26 + 111*x^25 + 110*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 58*x^20 + 61*x^19 + 60*x^18 + 27*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 39*x^11 + 12*x^10 + 49*x^9 + 34*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 70*x^4 + 27*x^3 + 84*x^2 + 109*x + 98, x^95 + 15*x^93 + 10*x^92 + 37*x^91 + 116*x^90 + 35*x^89 + 78*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 42*x^84 + 89*x^83 + 44*x^82 + 127*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 67*x^75 + 28*x^74 + 85*x^73 + 114*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 102*x^68 + 103*x^67 + 4*x^66 + 97*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 25*x^27 + 4*x^26 + 79*x^25 + 6*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 18*x^20 + 125*x^19 + 28*x^18 + 59*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 103*x^11 + 44*x^10 + 81*x^9 + 10*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 46*x^4 + 91*x^3 + 116*x^2 + 77*x + 106, x^95 + 15*x^93 + 62*x^92 + 53*x^91 + 124*x^90 + 51*x^89 + 10*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 30*x^84 + 9*x^83 + 100*x^82 + 47*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 115*x^75 + 52*x^74 + 5*x^73 + 54*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 18*x^68 + 119*x^67 + 44*x^66 + 113*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 105*x^27 + 44*x^26 + 31*x^25 + 50*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 86*x^20 + 109*x^19 + 52*x^18 + 43*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 87*x^11 + 100*x^10 + 65*x^9 + 126*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 106*x^4 + 43*x^3 + 124*x^2 + 29*x + 30, x^95 + 15*x^93 + 6*x^92 + 21*x^91 + 60*x^90 + 51*x^89 + 18*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 6*x^84 + 41*x^83 + 100*x^82 + 47*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 19*x^75 + 116*x^74 + 5*x^73 + 110*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 42*x^68 + 87*x^67 + 44*x^66 + 113*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 73*x^27 + 108*x^26 + 31*x^25 + 90*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 94*x^20 + 13*x^19 + 52*x^18 + 43*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 119*x^11 + 36*x^10 + 65*x^9 + 86*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 34*x^4 + 11*x^3 + 124*x^2 + 29*x + 22, x^95 + 15*x^93 + 46*x^92 + 101*x^91 + 12*x^90 + 3*x^89 + 106*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 110*x^84 + 25*x^83 + 20*x^82 + 31*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 3*x^75 + 100*x^74 + 117*x^73 + 22*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 2*x^68 + 39*x^67 + 60*x^66 + 65*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 89*x^27 + 124*x^26 + 47*x^25 + 18*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 102*x^20 + 61*x^19 + 36*x^18 + 91*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 39*x^11 + 84*x^10 + 113*x^9 + 94*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 26*x^4 + 27*x^3 + 76*x^2 + 45*x + 94, x^95 + 15*x^93 + 74*x^92 + 69*x^91 + 84*x^90 + 67*x^89 + 110*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 42*x^84 + 57*x^83 + 76*x^82 + 95*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 35*x^75 + 60*x^74 + 53*x^73 + 82*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 102*x^68 + 7*x^67 + 100*x^66 + x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 57*x^27 + 100*x^26 + 111*x^25 + 38*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 18*x^20 + 93*x^19 + 60*x^18 + 27*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 71*x^11 + 76*x^10 + 49*x^9 + 106*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 46*x^4 + 123*x^3 + 84*x^2 + 109*x + 10, x^95 + 15*x^93 + 26*x^92 + 53*x^91 + 4*x^90 + 19*x^89 + 78*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 26*x^84 + 9*x^83 + 92*x^82 + 79*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 115*x^75 + 76*x^74 + 37*x^73 + 50*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 54*x^68 + 119*x^67 + 20*x^66 + 81*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 105*x^27 + 84*x^26 + 127*x^25 + 6*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 66*x^20 + 109*x^19 + 12*x^18 + 75*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 87*x^11 + 28*x^10 + 97*x^9 + 74*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 62*x^4 + 43*x^3 + 68*x^2 + 125*x + 10, x^95 + 15*x^93 + 126*x^92 + 37*x^91 + 76*x^90 + 67*x^89 + 58*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 126*x^84 + 89*x^83 + 84*x^82 + 95*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 67*x^75 + 36*x^74 + 53*x^73 + 70*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 114*x^68 + 103*x^67 + 124*x^66 + x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 25*x^27 + 60*x^26 + 111*x^25 + 34*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 54*x^20 + 125*x^19 + 100*x^18 + 27*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 103*x^11 + 20*x^10 + 49*x^9 + 78*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 74*x^4 + 91*x^3 + 12*x^2 + 109*x + 14, x^95 + 15*x^93 + 70*x^92 + 53*x^91 + 92*x^90 + 83*x^89 + 114*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 6*x^84 + 9*x^83 + 68*x^82 + 15*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 115*x^75 + 84*x^74 + 101*x^73 + 14*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 42*x^68 + 119*x^67 + 76*x^66 + 17*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 105*x^27 + 12*x^26 + 63*x^25 + 58*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 94*x^20 + 109*x^19 + 20*x^18 + 11*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 87*x^11 + 4*x^10 + 33*x^9 + 118*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 34*x^4 + 43*x^3 + 28*x^2 + 61*x + 118, x^95 + 15*x^93 + 22*x^92 + 117*x^91 + 124*x^90 + 83*x^89 + 34*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 86*x^84 + 73*x^83 + 36*x^82 + 15*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 51*x^75 + 52*x^74 + 101*x^73 + 94*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 90*x^68 + 55*x^67 + 108*x^66 + 17*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 41*x^27 + 44*x^26 + 63*x^25 + 42*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 110*x^20 + 45*x^19 + 116*x^18 + 11*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 23*x^11 + 100*x^10 + 33*x^9 + 6*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 18*x^4 + 107*x^3 + 60*x^2 + 61*x + 6, x^95 + 15*x^93 + 18*x^92 + 37*x^91 + 116*x^90 + 67*x^89 + 86*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 82*x^84 + 89*x^83 + 108*x^82 + 95*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 67*x^75 + 28*x^74 + 53*x^73 + 42*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 62*x^68 + 103*x^67 + 68*x^66 + x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 25*x^27 + 4*x^26 + 111*x^25 + 46*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 90*x^20 + 125*x^19 + 92*x^18 + 27*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 103*x^11 + 44*x^10 + 49*x^9 + 98*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 38*x^4 + 91*x^3 + 52*x^2 + 109*x + 98, x^95 + 15*x^93 + 102*x^92 + 85*x^91 + 60*x^90 + 51*x^89 + 50*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 102*x^84 + 105*x^83 + 100*x^82 + 47*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 83*x^75 + 116*x^74 + 5*x^73 + 78*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 74*x^68 + 23*x^67 + 44*x^66 + 113*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 9*x^27 + 108*x^26 + 31*x^25 + 122*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 62*x^20 + 77*x^19 + 52*x^18 + 43*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 55*x^11 + 36*x^10 + 65*x^9 + 54*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 66*x^4 + 75*x^3 + 124*x^2 + 29*x + 118, x^95 + 15*x^93 + 94*x^92 + 5*x^91 + 76*x^90 + 35*x^89 + 90*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 94*x^84 + 121*x^83 + 84*x^82 + 127*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 99*x^75 + 36*x^74 + 85*x^73 + 38*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 18*x^68 + 71*x^67 + 124*x^66 + 97*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 121*x^27 + 60*x^26 + 79*x^25 + 66*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 22*x^20 + 29*x^19 + 100*x^18 + 59*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 7*x^11 + 20*x^10 + 81*x^9 + 46*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 106*x^4 + 59*x^3 + 12*x^2 + 77*x + 110, x^95 + 15*x^93 + 98*x^92 + 5*x^91 + 20*x^90 + 99*x^89 + 70*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 34*x^84 + 121*x^83 + 76*x^82 + 63*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 99*x^75 + 124*x^74 + 21*x^73 + 58*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 110*x^68 + 71*x^67 + 100*x^66 + 33*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 121*x^27 + 36*x^26 + 15*x^25 + 94*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 106*x^20 + 29*x^19 + 60*x^18 + 123*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 7*x^11 + 12*x^10 + 17*x^9 + 50*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 22*x^4 + 59*x^3 + 84*x^2 + 13*x + 50, x^95 + 15*x^93 + 110*x^92 + 117*x^91 + 28*x^90 + 51*x^89 + 26*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 78*x^84 + 73*x^83 + 68*x^82 + 47*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 51*x^75 + 20*x^74 + 5*x^73 + 38*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 98*x^68 + 55*x^67 + 76*x^66 + 113*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 41*x^27 + 76*x^26 + 31*x^25 + 2*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 70*x^20 + 45*x^19 + 20*x^18 + 43*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 23*x^11 + 68*x^10 + 65*x^9 + 46*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 122*x^4 + 107*x^3 + 28*x^2 + 29*x + 78, x^95 + 15*x^93 + 106*x^92 + 37*x^91 + 116*x^90 + 99*x^89 + 110*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 10*x^84 + 89*x^83 + 44*x^82 + 63*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 67*x^75 + 28*x^74 + 21*x^73 + 82*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 6*x^68 + 103*x^67 + 4*x^66 + 33*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 25*x^27 + 4*x^26 + 15*x^25 + 38*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 114*x^20 + 125*x^19 + 28*x^18 + 123*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 103*x^11 + 44*x^10 + 17*x^9 + 106*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 78*x^4 + 91*x^3 + 116*x^2 + 13*x + 74, x^95 + 15*x^93 + 18*x^92 + 69*x^91 + 116*x^90 + 99*x^89 + 22*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 82*x^84 + 57*x^83 + 108*x^82 + 63*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 35*x^75 + 28*x^74 + 21*x^73 + 106*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 62*x^68 + 7*x^67 + 68*x^66 + 33*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 57*x^27 + 4*x^26 + 15*x^25 + 110*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 90*x^20 + 93*x^19 + 92*x^18 + 123*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 71*x^11 + 44*x^10 + 17*x^9 + 34*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 38*x^4 + 123*x^3 + 52*x^2 + 13*x + 34, x^95 + 15*x^93 + 18*x^92 + 53*x^91 + 4*x^90 + 51*x^89 + 6*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 114*x^84 + 9*x^83 + 28*x^82 + 47*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 115*x^75 + 76*x^74 + 5*x^73 + 58*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 94*x^68 + 119*x^67 + 84*x^66 + 113*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 105*x^27 + 84*x^26 + 31*x^25 + 30*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 122*x^20 + 109*x^19 + 76*x^18 + 43*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 87*x^11 + 28*x^10 + 65*x^9 + 50*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 70*x^4 + 43*x^3 + 4*x^2 + 29*x + 82, x^95 + 15*x^93 + 74*x^92 + 53*x^91 + 4*x^90 + 19*x^89 + 62*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 10*x^84 + 9*x^83 + 92*x^82 + 79*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 115*x^75 + 76*x^74 + 37*x^73 + 66*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 70*x^68 + 119*x^67 + 20*x^66 + 81*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 105*x^27 + 84*x^26 + 127*x^25 + 54*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 114*x^20 + 109*x^19 + 12*x^18 + 75*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 87*x^11 + 28*x^10 + 97*x^9 + 26*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 14*x^4 + 43*x^3 + 68*x^2 + 125*x + 26, x^95 + 15*x^93 + 102*x^92 + 69*x^91 + 12*x^90 + 3*x^89 + 98*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 6*x^84 + 57*x^83 + 84*x^82 + 31*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 35*x^75 + 100*x^74 + 117*x^73 + 94*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 106*x^68 + 7*x^67 + 124*x^66 + 65*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 57*x^27 + 124*x^26 + 47*x^25 + 106*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 94*x^20 + 93*x^19 + 100*x^18 + 91*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 71*x^11 + 84*x^10 + 113*x^9 + 6*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 98*x^4 + 123*x^3 + 12*x^2 + 45*x + 102, x^95 + 15*x^93 + 102*x^92 + 101*x^91 + 44*x^90 + 99*x^89 + 66*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 70*x^84 + 25*x^83 + 52*x^82 + 63*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 3*x^75 + 68*x^74 + 21*x^73 + 126*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 42*x^68 + 39*x^67 + 28*x^66 + 33*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 89*x^27 + 28*x^26 + 15*x^25 + 74*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 30*x^20 + 61*x^19 + 68*x^18 + 123*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 39*x^11 + 52*x^10 + 17*x^9 + 38*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 34*x^4 + 27*x^3 + 44*x^2 + 13*x + 70, x^95 + 15*x^93 + 46*x^92 + 5*x^91 + 12*x^90 + 35*x^89 + 42*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 110*x^84 + 121*x^83 + 20*x^82 + 127*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 99*x^75 + 100*x^74 + 85*x^73 + 86*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 2*x^68 + 71*x^67 + 60*x^66 + 97*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 121*x^27 + 124*x^26 + 79*x^25 + 82*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 102*x^20 + 29*x^19 + 36*x^18 + 59*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 7*x^11 + 84*x^10 + 81*x^9 + 30*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 26*x^4 + 59*x^3 + 76*x^2 + 77*x + 30, x^95 + 15*x^93 + 102*x^92 + 5*x^91 + 108*x^90 + 3*x^89 + 66*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 70*x^84 + 121*x^83 + 116*x^82 + 31*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 99*x^75 + 4*x^74 + 117*x^73 + 126*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 42*x^68 + 71*x^67 + 92*x^66 + 65*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 121*x^27 + 92*x^26 + 47*x^25 + 74*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 30*x^20 + 29*x^19 + 4*x^18 + 91*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 7*x^11 + 116*x^10 + 113*x^9 + 38*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 34*x^4 + 59*x^3 + 108*x^2 + 45*x + 70, x^95 + 15*x^93 + 18*x^92 + 37*x^91 + 84*x^90 + 3*x^89 + 54*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 18*x^84 + 89*x^83 + 12*x^82 + 31*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 67*x^75 + 60*x^74 + 117*x^73 + 74*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 126*x^68 + 103*x^67 + 36*x^66 + 65*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 25*x^27 + 100*x^26 + 47*x^25 + 14*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 26*x^20 + 125*x^19 + 124*x^18 + 91*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 103*x^11 + 76*x^10 + 113*x^9 + 2*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 102*x^4 + 91*x^3 + 20*x^2 + 45*x + 66, x^95 + 15*x^93 + 30*x^92 + 69*x^91 + 44*x^90 + 35*x^89 + 122*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 94*x^84 + 57*x^83 + 116*x^82 + 127*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 35*x^75 + 68*x^74 + 85*x^73 + 6*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 18*x^68 + 7*x^67 + 92*x^66 + 97*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 57*x^27 + 28*x^26 + 79*x^25 + 98*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 22*x^20 + 93*x^19 + 4*x^18 + 59*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 71*x^11 + 52*x^10 + 81*x^9 + 14*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 106*x^4 + 123*x^3 + 108*x^2 + 77*x + 14, x^95 + 15*x^93 + 58*x^92 + 117*x^91 + 4*x^90 + 19*x^89 + 46*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 58*x^84 + 73*x^83 + 92*x^82 + 79*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 51*x^75 + 76*x^74 + 37*x^73 + 82*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 22*x^68 + 55*x^67 + 20*x^66 + 81*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 41*x^27 + 84*x^26 + 127*x^25 + 102*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 98*x^20 + 45*x^19 + 12*x^18 + 75*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 23*x^11 + 28*x^10 + 97*x^9 + 106*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 30*x^4 + 107*x^3 + 68*x^2 + 125*x + 42, x^95 + 15*x^93 + 54*x^92 + 53*x^91 + 124*x^90 + 19*x^89 + 66*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 118*x^84 + 9*x^83 + 36*x^82 + 79*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 115*x^75 + 52*x^74 + 37*x^73 + 62*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 58*x^68 + 119*x^67 + 108*x^66 + 81*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 105*x^27 + 44*x^26 + 127*x^25 + 74*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 14*x^20 + 109*x^19 + 116*x^18 + 75*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 87*x^11 + 100*x^10 + 97*x^9 + 102*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 114*x^4 + 43*x^3 + 60*x^2 + 125*x + 102, x^95 + 15*x^93 + 46*x^92 + 117*x^91 + 124*x^90 + 115*x^89 + 58*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 78*x^84 + 73*x^83 + 100*x^82 + 111*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 51*x^75 + 52*x^74 + 69*x^73 + 6*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 98*x^68 + 55*x^67 + 44*x^66 + 49*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 41*x^27 + 44*x^26 + 95*x^25 + 34*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 70*x^20 + 45*x^19 + 52*x^18 + 107*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 23*x^11 + 100*x^10 + x^9 + 14*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 122*x^4 + 107*x^3 + 124*x^2 + 93*x + 110, x^95 + 15*x^93 + 34*x^92 + 37*x^91 + 116*x^90 + 3*x^89 + 102*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 34*x^84 + 89*x^83 + 108*x^82 + 31*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 67*x^75 + 28*x^74 + 117*x^73 + 26*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 110*x^68 + 103*x^67 + 68*x^66 + 65*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 25*x^27 + 4*x^26 + 47*x^25 + 126*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 106*x^20 + 125*x^19 + 92*x^18 + 91*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 103*x^11 + 44*x^10 + 113*x^9 + 18*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 22*x^4 + 91*x^3 + 52*x^2 + 45*x + 82, x^95 + 15*x^93 + 50*x^92 + 53*x^91 + 100*x^90 + 51*x^89 + 70*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 82*x^84 + 9*x^83 + 60*x^82 + 47*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 115*x^75 + 108*x^74 + 5*x^73 + 122*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 126*x^68 + 119*x^67 + 52*x^66 + 113*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 105*x^27 + 52*x^26 + 31*x^25 + 94*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 90*x^20 + 109*x^19 + 108*x^18 + 43*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 87*x^11 + 60*x^10 + 65*x^9 + 114*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 102*x^4 + 43*x^3 + 100*x^2 + 29*x + 82, x^95 + 15*x^93 + 6*x^92 + 5*x^91 + 12*x^90 + 3*x^89 + 66*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 38*x^84 + 121*x^83 + 84*x^82 + 31*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 99*x^75 + 100*x^74 + 117*x^73 + 126*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 74*x^68 + 71*x^67 + 124*x^66 + 65*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 121*x^27 + 124*x^26 + 47*x^25 + 74*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 126*x^20 + 29*x^19 + 100*x^18 + 91*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 7*x^11 + 84*x^10 + 113*x^9 + 38*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 66*x^4 + 59*x^3 + 12*x^2 + 45*x + 6, x^95 + 15*x^93 + 54*x^92 + 5*x^91 + 12*x^90 + 67*x^89 + 114*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 22*x^84 + 121*x^83 + 84*x^82 + 95*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 99*x^75 + 100*x^74 + 53*x^73 + 78*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 90*x^68 + 71*x^67 + 124*x^66 + x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 121*x^27 + 124*x^26 + 111*x^25 + 58*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 46*x^20 + 29*x^19 + 100*x^18 + 27*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 7*x^11 + 84*x^10 + 49*x^9 + 54*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 18*x^4 + 59*x^3 + 12*x^2 + 109*x + 86, x^95 + 15*x^93 + 14*x^92 + 37*x^91 + 108*x^90 + 3*x^89 + 42*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 14*x^84 + 89*x^83 + 52*x^82 + 31*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 67*x^75 + 4*x^74 + 117*x^73 + 86*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 98*x^68 + 103*x^67 + 28*x^66 + 65*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 25*x^27 + 92*x^26 + 47*x^25 + 82*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 6*x^20 + 125*x^19 + 68*x^18 + 91*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 103*x^11 + 116*x^10 + 113*x^9 + 30*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 122*x^4 + 91*x^3 + 44*x^2 + 45*x + 94, x^95 + 15*x^93 + 110*x^92 + 37*x^91 + 108*x^90 + 3*x^89 + 10*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 110*x^84 + 89*x^83 + 52*x^82 + 31*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 67*x^75 + 4*x^74 + 117*x^73 + 118*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 2*x^68 + 103*x^67 + 28*x^66 + 65*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 25*x^27 + 92*x^26 + 47*x^25 + 50*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 102*x^20 + 125*x^19 + 68*x^18 + 91*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 103*x^11 + 116*x^10 + 113*x^9 + 62*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 26*x^4 + 91*x^3 + 44*x^2 + 45*x + 126, x^95 + 15*x^93 + 22*x^92 + 5*x^91 + 44*x^90 + 3*x^89 + 114*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 54*x^84 + 121*x^83 + 52*x^82 + 31*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 99*x^75 + 68*x^74 + 117*x^73 + 78*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 58*x^68 + 71*x^67 + 28*x^66 + 65*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 121*x^27 + 28*x^26 + 47*x^25 + 58*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 78*x^20 + 29*x^19 + 68*x^18 + 91*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 7*x^11 + 52*x^10 + 113*x^9 + 54*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 114*x^4 + 59*x^3 + 44*x^2 + 45*x + 22, x^95 + 15*x^93 + 78*x^92 + 101*x^91 + 12*x^90 + 67*x^89 + 74*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 14*x^84 + 25*x^83 + 20*x^82 + 95*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 3*x^75 + 100*x^74 + 53*x^73 + 54*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 98*x^68 + 39*x^67 + 60*x^66 + x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 89*x^27 + 124*x^26 + 111*x^25 + 114*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 6*x^20 + 61*x^19 + 36*x^18 + 27*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 39*x^11 + 84*x^10 + 49*x^9 + 126*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 122*x^4 + 27*x^3 + 76*x^2 + 109*x + 126, x^95 + 15*x^93 + 114*x^92 + 37*x^91 + 116*x^90 + 3*x^89 + 118*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 50*x^84 + 89*x^83 + 108*x^82 + 31*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 67*x^75 + 28*x^74 + 117*x^73 + 10*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 94*x^68 + 103*x^67 + 68*x^66 + 65*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 25*x^27 + 4*x^26 + 47*x^25 + 78*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 58*x^20 + 125*x^19 + 92*x^18 + 91*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 103*x^11 + 44*x^10 + 113*x^9 + 66*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 70*x^4 + 91*x^3 + 52*x^2 + 45*x + 66, x^95 + 15*x^93 + 122*x^92 + 101*x^91 + 84*x^90 + 99*x^89 + 30*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 26*x^84 + 25*x^83 + 76*x^82 + 63*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 3*x^75 + 60*x^74 + 21*x^73 + 34*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 118*x^68 + 39*x^67 + 100*x^66 + 33*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 89*x^27 + 100*x^26 + 15*x^25 + 22*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 66*x^20 + 61*x^19 + 60*x^18 + 123*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 39*x^11 + 76*x^10 + 17*x^9 + 122*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 126*x^4 + 27*x^3 + 84*x^2 + 13*x + 90, x^95 + 15*x^93 + 22*x^92 + 37*x^91 + 108*x^90 + 99*x^89 + 50*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 54*x^84 + 89*x^83 + 116*x^82 + 63*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 67*x^75 + 4*x^74 + 21*x^73 + 14*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 58*x^68 + 103*x^67 + 92*x^66 + 33*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 25*x^27 + 92*x^26 + 15*x^25 + 122*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 78*x^20 + 125*x^19 + 4*x^18 + 123*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 103*x^11 + 116*x^10 + 17*x^9 + 118*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 114*x^4 + 91*x^3 + 108*x^2 + 13*x + 86, x^95 + 15*x^93 + 10*x^92 + 37*x^91 + 52*x^90 + 35*x^89 + 14*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 42*x^84 + 89*x^83 + 108*x^82 + 127*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 67*x^75 + 92*x^74 + 85*x^73 + 50*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 102*x^68 + 103*x^67 + 68*x^66 + 97*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 25*x^27 + 68*x^26 + 79*x^25 + 70*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 18*x^20 + 125*x^19 + 92*x^18 + 59*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 103*x^11 + 108*x^10 + 81*x^9 + 74*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 46*x^4 + 91*x^3 + 52*x^2 + 77*x + 42, x^95 + 15*x^93 + 106*x^92 + 21*x^91 + 36*x^90 + 51*x^89 + 62*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 106*x^84 + 41*x^83 + 60*x^82 + 47*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 19*x^75 + 44*x^74 + 5*x^73 + 66*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 102*x^68 + 87*x^67 + 52*x^66 + 113*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 73*x^27 + 116*x^26 + 31*x^25 + 54*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 82*x^20 + 13*x^19 + 108*x^18 + 43*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 119*x^11 + 124*x^10 + 65*x^9 + 26*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 46*x^4 + 11*x^3 + 100*x^2 + 29*x + 90, x^95 + 15*x^93 + 114*x^92 + 101*x^91 + 84*x^90 + 67*x^89 + 22*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 114*x^84 + 25*x^83 + 12*x^82 + 95*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 3*x^75 + 60*x^74 + 53*x^73 + 106*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 30*x^68 + 39*x^67 + 36*x^66 + x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 89*x^27 + 100*x^26 + 111*x^25 + 110*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 122*x^20 + 61*x^19 + 124*x^18 + 27*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 39*x^11 + 76*x^10 + 49*x^9 + 34*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 6*x^4 + 27*x^3 + 20*x^2 + 109*x + 98, x^95 + 15*x^93 + 102*x^92 + 117*x^91 + 28*x^90 + 83*x^89 + 18*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 38*x^84 + 73*x^83 + 4*x^82 + 15*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 51*x^75 + 20*x^74 + 101*x^73 + 110*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 10*x^68 + 55*x^67 + 12*x^66 + 17*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 41*x^27 + 76*x^26 + 63*x^25 + 90*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 126*x^20 + 45*x^19 + 84*x^18 + 11*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 23*x^11 + 68*x^10 + 33*x^9 + 86*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 2*x^4 + 107*x^3 + 92*x^2 + 61*x + 86, x^95 + 15*x^93 + 110*x^92 + 5*x^91 + 12*x^90 + 35*x^89 + 106*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 46*x^84 + 121*x^83 + 20*x^82 + 127*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 99*x^75 + 100*x^74 + 85*x^73 + 22*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 66*x^68 + 71*x^67 + 60*x^66 + 97*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 121*x^27 + 124*x^26 + 79*x^25 + 18*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 38*x^20 + 29*x^19 + 36*x^18 + 59*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 7*x^11 + 84*x^10 + 81*x^9 + 94*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 90*x^4 + 59*x^3 + 76*x^2 + 77*x + 94, x^95 + 15*x^93 + 102*x^92 + 21*x^91 + 60*x^90 + 51*x^89 + 114*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 102*x^84 + 41*x^83 + 100*x^82 + 47*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 19*x^75 + 116*x^74 + 5*x^73 + 14*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 74*x^68 + 87*x^67 + 44*x^66 + 113*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 73*x^27 + 108*x^26 + 31*x^25 + 58*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 62*x^20 + 13*x^19 + 52*x^18 + 43*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 119*x^11 + 36*x^10 + 65*x^9 + 118*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 66*x^4 + 11*x^3 + 124*x^2 + 29*x + 54, x^95 + 15*x^93 + 110*x^92 + 101*x^91 + 108*x^90 + 67*x^89 + 10*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 110*x^84 + 25*x^83 + 52*x^82 + 95*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 3*x^75 + 4*x^74 + 53*x^73 + 118*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 2*x^68 + 39*x^67 + 28*x^66 + x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 89*x^27 + 92*x^26 + 111*x^25 + 50*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 102*x^20 + 61*x^19 + 68*x^18 + 27*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 39*x^11 + 116*x^10 + 49*x^9 + 62*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 26*x^4 + 27*x^3 + 44*x^2 + 109*x + 126, x^95 + 15*x^93 + 58*x^92 + 85*x^91 + 68*x^90 + 115*x^89 + 46*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 58*x^84 + 105*x^83 + 28*x^82 + 111*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 83*x^75 + 12*x^74 + 69*x^73 + 82*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 22*x^68 + 23*x^67 + 84*x^66 + 49*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 9*x^27 + 20*x^26 + 95*x^25 + 102*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 98*x^20 + 77*x^19 + 76*x^18 + 107*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 55*x^11 + 92*x^10 + x^9 + 106*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 30*x^4 + 75*x^3 + 4*x^2 + 93*x + 42, x^95 + 15*x^93 + 90*x^92 + 21*x^91 + 68*x^90 + 115*x^89 + 14*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 90*x^84 + 41*x^83 + 28*x^82 + 111*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 19*x^75 + 12*x^74 + 69*x^73 + 114*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 118*x^68 + 87*x^67 + 84*x^66 + 49*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 73*x^27 + 20*x^26 + 95*x^25 + 70*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 2*x^20 + 13*x^19 + 76*x^18 + 107*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 119*x^11 + 92*x^10 + x^9 + 10*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 126*x^4 + 11*x^3 + 4*x^2 + 93*x + 74, x^95 + 15*x^93 + 114*x^92 + 101*x^91 + 116*x^90 + 67*x^89 + 118*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 50*x^84 + 25*x^83 + 108*x^82 + 95*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 3*x^75 + 28*x^74 + 53*x^73 + 10*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 94*x^68 + 39*x^67 + 68*x^66 + x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 89*x^27 + 4*x^26 + 111*x^25 + 78*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 58*x^20 + 61*x^19 + 92*x^18 + 27*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 39*x^11 + 44*x^10 + 49*x^9 + 66*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 70*x^4 + 27*x^3 + 52*x^2 + 109*x + 66, x^95 + 15*x^93 + 66*x^92 + 53*x^91 + 4*x^90 + 51*x^89 + 118*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 98*x^84 + 9*x^83 + 28*x^82 + 47*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 115*x^75 + 76*x^74 + 5*x^73 + 74*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 110*x^68 + 119*x^67 + 84*x^66 + 113*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 105*x^27 + 84*x^26 + 31*x^25 + 78*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 42*x^20 + 109*x^19 + 76*x^18 + 43*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 87*x^11 + 28*x^10 + 65*x^9 + 2*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 22*x^4 + 43*x^3 + 4*x^2 + 29*x + 98, x^95 + 15*x^93 + 66*x^92 + 101*x^91 + 52*x^90 + 3*x^89 + 6*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 66*x^84 + 25*x^83 + 44*x^82 + 31*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 3*x^75 + 92*x^74 + 117*x^73 + 122*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 78*x^68 + 39*x^67 + 4*x^66 + 65*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 89*x^27 + 68*x^26 + 47*x^25 + 30*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 10*x^20 + 61*x^19 + 28*x^18 + 91*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 39*x^11 + 108*x^10 + 113*x^9 + 114*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 118*x^4 + 27*x^3 + 116*x^2 + 45*x + 50, x^95 + 15*x^93 + 14*x^92 + 117*x^91 + 28*x^90 + 51*x^89 + 58*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 110*x^84 + 73*x^83 + 68*x^82 + 47*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 51*x^75 + 20*x^74 + 5*x^73 + 6*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 66*x^68 + 55*x^67 + 76*x^66 + 113*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 41*x^27 + 76*x^26 + 31*x^25 + 34*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 102*x^20 + 45*x^19 + 20*x^18 + 43*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 23*x^11 + 68*x^10 + 65*x^9 + 14*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 90*x^4 + 107*x^3 + 28*x^2 + 29*x + 46, x^95 + 15*x^93 + 94*x^92 + 85*x^91 + 60*x^90 + 19*x^89 + 106*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 62*x^84 + 105*x^83 + 36*x^82 + 79*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 83*x^75 + 116*x^74 + 37*x^73 + 86*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 114*x^68 + 23*x^67 + 108*x^66 + 81*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 9*x^27 + 108*x^26 + 127*x^25 + 18*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 118*x^20 + 77*x^19 + 116*x^18 + 75*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 55*x^11 + 36*x^10 + 97*x^9 + 30*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 74*x^4 + 75*x^3 + 60*x^2 + 125*x + 62, x^95 + 15*x^93 + 50*x^92 + 101*x^91 + 84*x^90 + 3*x^89 + 22*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 50*x^84 + 25*x^83 + 12*x^82 + 31*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 3*x^75 + 60*x^74 + 117*x^73 + 106*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 94*x^68 + 39*x^67 + 36*x^66 + 65*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 89*x^27 + 100*x^26 + 47*x^25 + 110*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 58*x^20 + 61*x^19 + 124*x^18 + 91*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 39*x^11 + 76*x^10 + 113*x^9 + 34*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 70*x^4 + 27*x^3 + 20*x^2 + 45*x + 98, x^95 + 15*x^93 + 86*x^92 + 101*x^91 + 12*x^90 + 99*x^89 + 18*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 54*x^84 + 25*x^83 + 84*x^82 + 63*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 3*x^75 + 100*x^74 + 21*x^73 + 46*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 58*x^68 + 39*x^67 + 124*x^66 + 33*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 89*x^27 + 124*x^26 + 15*x^25 + 90*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 78*x^20 + 61*x^19 + 100*x^18 + 123*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 39*x^11 + 84*x^10 + 17*x^9 + 22*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 114*x^4 + 27*x^3 + 12*x^2 + 13*x + 54, x^95 + 15*x^93 + 94*x^92 + 5*x^91 + 44*x^90 + 99*x^89 + 58*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 30*x^84 + 121*x^83 + 116*x^82 + 63*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 99*x^75 + 68*x^74 + 21*x^73 + 70*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 82*x^68 + 71*x^67 + 92*x^66 + 33*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 121*x^27 + 28*x^26 + 15*x^25 + 34*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 86*x^20 + 29*x^19 + 4*x^18 + 123*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 7*x^11 + 52*x^10 + 17*x^9 + 78*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 42*x^4 + 59*x^3 + 108*x^2 + 13*x + 78, x^95 + 15*x^93 + 26*x^92 + 37*x^91 + 20*x^90 + 99*x^89 + 62*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 58*x^84 + 89*x^83 + 12*x^82 + 63*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 67*x^75 + 124*x^74 + 21*x^73 + 2*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 86*x^68 + 103*x^67 + 36*x^66 + 33*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 25*x^27 + 36*x^26 + 15*x^25 + 54*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 98*x^20 + 125*x^19 + 124*x^18 + 123*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 103*x^11 + 12*x^10 + 17*x^9 + 90*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 94*x^4 + 91*x^3 + 20*x^2 + 13*x + 58, x^95 + 15*x^93 + 106*x^92 + 5*x^91 + 116*x^90 + 3*x^89 + 110*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 10*x^84 + 121*x^83 + 44*x^82 + 31*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 99*x^75 + 28*x^74 + 117*x^73 + 82*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 6*x^68 + 71*x^67 + 4*x^66 + 65*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 121*x^27 + 4*x^26 + 47*x^25 + 38*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 114*x^20 + 29*x^19 + 28*x^18 + 91*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 7*x^11 + 44*x^10 + 113*x^9 + 106*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 78*x^4 + 59*x^3 + 116*x^2 + 45*x + 74, x^95 + 15*x^93 + 54*x^92 + 85*x^91 + 92*x^90 + 51*x^89 + 34*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 54*x^84 + 105*x^83 + 68*x^82 + 47*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 83*x^75 + 84*x^74 + 5*x^73 + 94*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 122*x^68 + 23*x^67 + 76*x^66 + 113*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 9*x^27 + 12*x^26 + 31*x^25 + 42*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 78*x^20 + 77*x^19 + 20*x^18 + 43*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 55*x^11 + 4*x^10 + 65*x^9 + 6*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 50*x^4 + 75*x^3 + 28*x^2 + 29*x + 70, x^95 + 15*x^93 + 34*x^92 + 37*x^91 + 20*x^90 + 67*x^89 + 6*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 98*x^84 + 89*x^83 + 76*x^82 + 95*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 67*x^75 + 124*x^74 + 53*x^73 + 122*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 46*x^68 + 103*x^67 + 100*x^66 + x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 25*x^27 + 36*x^26 + 111*x^25 + 30*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 42*x^20 + 125*x^19 + 60*x^18 + 27*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 103*x^11 + 12*x^10 + 49*x^9 + 114*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 86*x^4 + 91*x^3 + 84*x^2 + 109*x + 114, x^95 + 15*x^93 + 34*x^92 + 21*x^91 + 100*x^90 + 19*x^89 + 54*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 2*x^84 + 41*x^83 + 60*x^82 + 79*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 19*x^75 + 108*x^74 + 37*x^73 + 10*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 78*x^68 + 87*x^67 + 52*x^66 + 81*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 73*x^27 + 52*x^26 + 127*x^25 + 14*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 74*x^20 + 13*x^19 + 108*x^18 + 75*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 119*x^11 + 60*x^10 + 97*x^9 + 66*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 118*x^4 + 11*x^3 + 100*x^2 + 125*x + 98, x^95 + 15*x^93 + 38*x^92 + 37*x^91 + 76*x^90 + 99*x^89 + 34*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 70*x^84 + 89*x^83 + 20*x^82 + 63*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 67*x^75 + 36*x^74 + 21*x^73 + 30*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 42*x^68 + 103*x^67 + 60*x^66 + 33*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 25*x^27 + 60*x^26 + 15*x^25 + 42*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 30*x^20 + 125*x^19 + 36*x^18 + 123*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 103*x^11 + 20*x^10 + 17*x^9 + 70*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 34*x^4 + 91*x^3 + 76*x^2 + 13*x + 38, x^95 + 15*x^93 + 94*x^92 + 69*x^91 + 12*x^90 + 35*x^89 + 90*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 94*x^84 + 57*x^83 + 20*x^82 + 127*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 35*x^75 + 100*x^74 + 85*x^73 + 38*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 18*x^68 + 7*x^67 + 60*x^66 + 97*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 57*x^27 + 124*x^26 + 79*x^25 + 66*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 22*x^20 + 93*x^19 + 36*x^18 + 59*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 71*x^11 + 84*x^10 + 81*x^9 + 46*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 106*x^4 + 123*x^3 + 76*x^2 + 77*x + 110, x^95 + 15*x^93 + 98*x^92 + 69*x^91 + 20*x^90 + 35*x^89 + 70*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 34*x^84 + 57*x^83 + 76*x^82 + 127*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 35*x^75 + 124*x^74 + 85*x^73 + 58*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 110*x^68 + 7*x^67 + 100*x^66 + 97*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 57*x^27 + 36*x^26 + 79*x^25 + 94*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 106*x^20 + 93*x^19 + 60*x^18 + 59*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 71*x^11 + 12*x^10 + 81*x^9 + 50*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 22*x^4 + 123*x^3 + 84*x^2 + 77*x + 50, x^95 + 15*x^93 + 18*x^92 + 53*x^91 + 4*x^90 + 115*x^89 + 70*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 114*x^84 + 9*x^83 + 28*x^82 + 111*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 115*x^75 + 76*x^74 + 69*x^73 + 122*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 94*x^68 + 119*x^67 + 84*x^66 + 49*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 105*x^27 + 84*x^26 + 95*x^25 + 94*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 122*x^20 + 109*x^19 + 76*x^18 + 107*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 87*x^11 + 28*x^10 + x^9 + 114*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 70*x^4 + 43*x^3 + 4*x^2 + 93*x + 18, x^95 + 15*x^93 + 98*x^92 + 117*x^91 + 36*x^90 + 51*x^89 + 54*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 66*x^84 + 73*x^83 + 124*x^82 + 47*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 51*x^75 + 44*x^74 + 5*x^73 + 10*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 14*x^68 + 55*x^67 + 116*x^66 + 113*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 41*x^27 + 116*x^26 + 31*x^25 + 14*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 10*x^20 + 45*x^19 + 44*x^18 + 43*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 23*x^11 + 124*x^10 + 65*x^9 + 66*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 54*x^4 + 107*x^3 + 36*x^2 + 29*x + 98, x^95 + 15*x^93 + 30*x^92 + 69*x^91 + 108*x^90 + 35*x^89 + 58*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 94*x^84 + 57*x^83 + 52*x^82 + 127*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 35*x^75 + 4*x^74 + 85*x^73 + 70*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 18*x^68 + 7*x^67 + 28*x^66 + 97*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 57*x^27 + 92*x^26 + 79*x^25 + 34*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 22*x^20 + 93*x^19 + 68*x^18 + 59*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 71*x^11 + 116*x^10 + 81*x^9 + 78*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 106*x^4 + 123*x^3 + 44*x^2 + 77*x + 78, x^95 + 15*x^93 + 6*x^92 + 69*x^91 + 12*x^90 + 67*x^89 + 66*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 38*x^84 + 57*x^83 + 84*x^82 + 95*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 35*x^75 + 100*x^74 + 53*x^73 + 126*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 74*x^68 + 7*x^67 + 124*x^66 + x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 57*x^27 + 124*x^26 + 111*x^25 + 74*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 126*x^20 + 93*x^19 + 100*x^18 + 27*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 71*x^11 + 84*x^10 + 49*x^9 + 38*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 66*x^4 + 123*x^3 + 12*x^2 + 109*x + 6, x^95 + 15*x^93 + 82*x^92 + 53*x^91 + 100*x^90 + 51*x^89 + 102*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 114*x^84 + 9*x^83 + 60*x^82 + 47*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 115*x^75 + 108*x^74 + 5*x^73 + 90*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 94*x^68 + 119*x^67 + 52*x^66 + 113*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 105*x^27 + 52*x^26 + 31*x^25 + 126*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 122*x^20 + 109*x^19 + 108*x^18 + 43*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 87*x^11 + 60*x^10 + 65*x^9 + 82*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 70*x^4 + 43*x^3 + 100*x^2 + 29*x + 50, x^95 + 15*x^93 + 66*x^92 + 37*x^91 + 52*x^90 + 3*x^89 + 70*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 66*x^84 + 89*x^83 + 44*x^82 + 31*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 67*x^75 + 92*x^74 + 117*x^73 + 58*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 78*x^68 + 103*x^67 + 4*x^66 + 65*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 25*x^27 + 68*x^26 + 47*x^25 + 94*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 10*x^20 + 125*x^19 + 28*x^18 + 91*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 103*x^11 + 108*x^10 + 113*x^9 + 50*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 118*x^4 + 91*x^3 + 116*x^2 + 45*x + 114, x^95 + 15*x^93 + 62*x^92 + 69*x^91 + 12*x^90 + 35*x^89 + 58*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 62*x^84 + 57*x^83 + 20*x^82 + 127*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 35*x^75 + 100*x^74 + 85*x^73 + 70*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 50*x^68 + 7*x^67 + 60*x^66 + 97*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 57*x^27 + 124*x^26 + 79*x^25 + 34*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 118*x^20 + 93*x^19 + 36*x^18 + 59*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 71*x^11 + 84*x^10 + 81*x^9 + 78*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 10*x^4 + 123*x^3 + 76*x^2 + 77*x + 14, x^95 + 15*x^93 + 22*x^92 + 69*x^91 + 44*x^90 + 67*x^89 + 114*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 54*x^84 + 57*x^83 + 52*x^82 + 95*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 35*x^75 + 68*x^74 + 53*x^73 + 78*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 58*x^68 + 7*x^67 + 28*x^66 + x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 57*x^27 + 28*x^26 + 111*x^25 + 58*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 78*x^20 + 93*x^19 + 68*x^18 + 27*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 71*x^11 + 52*x^10 + 49*x^9 + 54*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 114*x^4 + 123*x^3 + 44*x^2 + 109*x + 22, x^95 + 15*x^93 + 22*x^92 + 5*x^91 + 44*x^90 + 67*x^89 + 50*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 54*x^84 + 121*x^83 + 52*x^82 + 95*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 99*x^75 + 68*x^74 + 53*x^73 + 14*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 58*x^68 + 71*x^67 + 28*x^66 + x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 121*x^27 + 28*x^26 + 111*x^25 + 122*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 78*x^20 + 29*x^19 + 68*x^18 + 27*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 7*x^11 + 52*x^10 + 49*x^9 + 118*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 114*x^4 + 59*x^3 + 44*x^2 + 109*x + 86, x^95 + 15*x^93 + 14*x^92 + 5*x^91 + 12*x^90 + 99*x^89 + 74*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 78*x^84 + 121*x^83 + 20*x^82 + 63*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 99*x^75 + 100*x^74 + 21*x^73 + 54*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 34*x^68 + 71*x^67 + 60*x^66 + 33*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 121*x^27 + 124*x^26 + 15*x^25 + 114*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 70*x^20 + 29*x^19 + 36*x^18 + 123*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 7*x^11 + 84*x^10 + 17*x^9 + 126*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 58*x^4 + 59*x^3 + 76*x^2 + 13*x + 126, x^95 + 15*x^93 + 126*x^92 + 53*x^91 + 124*x^90 + 115*x^89 + 10*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 94*x^84 + 9*x^83 + 100*x^82 + 111*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 115*x^75 + 52*x^74 + 69*x^73 + 54*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 82*x^68 + 119*x^67 + 44*x^66 + 49*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 105*x^27 + 44*x^26 + 95*x^25 + 50*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 22*x^20 + 109*x^19 + 52*x^18 + 107*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 87*x^11 + 100*x^10 + x^9 + 126*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 42*x^4 + 43*x^3 + 124*x^2 + 93*x + 30, x^95 + 15*x^93 + 86*x^92 + 21*x^91 + 60*x^90 + 115*x^89 + 98*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 22*x^84 + 41*x^83 + 100*x^82 + 111*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 19*x^75 + 116*x^74 + 69*x^73 + 30*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 26*x^68 + 87*x^67 + 44*x^66 + 49*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 73*x^27 + 108*x^26 + 95*x^25 + 106*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 46*x^20 + 13*x^19 + 52*x^18 + 107*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 119*x^11 + 36*x^10 + x^9 + 70*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 82*x^4 + 11*x^3 + 124*x^2 + 93*x + 70, x^95 + 15*x^93 + 58*x^92 + 37*x^91 + 84*x^90 + 35*x^89 + 94*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 90*x^84 + 89*x^83 + 76*x^82 + 127*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 67*x^75 + 60*x^74 + 85*x^73 + 98*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 54*x^68 + 103*x^67 + 100*x^66 + 97*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 25*x^27 + 100*x^26 + 79*x^25 + 86*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 2*x^20 + 125*x^19 + 60*x^18 + 59*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 103*x^11 + 76*x^10 + 81*x^9 + 58*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 62*x^4 + 91*x^3 + 84*x^2 + 77*x + 26, x^95 + 15*x^93 + 122*x^92 + 117*x^91 + 68*x^90 + 19*x^89 + 46*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 122*x^84 + 73*x^83 + 28*x^82 + 79*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 51*x^75 + 12*x^74 + 37*x^73 + 82*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 86*x^68 + 55*x^67 + 84*x^66 + 81*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 41*x^27 + 20*x^26 + 127*x^25 + 102*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 34*x^20 + 45*x^19 + 76*x^18 + 75*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 23*x^11 + 92*x^10 + 97*x^9 + 106*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 94*x^4 + 107*x^3 + 4*x^2 + 125*x + 42, x^95 + 15*x^93 + 70*x^92 + 53*x^91 + 28*x^90 + 83*x^89 + 50*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 6*x^84 + 9*x^83 + 4*x^82 + 15*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 115*x^75 + 20*x^74 + 101*x^73 + 78*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 42*x^68 + 119*x^67 + 12*x^66 + 17*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 105*x^27 + 76*x^26 + 63*x^25 + 122*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 94*x^20 + 109*x^19 + 84*x^18 + 11*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 87*x^11 + 68*x^10 + 33*x^9 + 54*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 34*x^4 + 43*x^3 + 92*x^2 + 61*x + 54, x^95 + 15*x^93 + 34*x^92 + 69*x^91 + 52*x^90 + 35*x^89 + 102*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 34*x^84 + 57*x^83 + 44*x^82 + 127*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 35*x^75 + 92*x^74 + 85*x^73 + 26*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 110*x^68 + 7*x^67 + 4*x^66 + 97*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 57*x^27 + 68*x^26 + 79*x^25 + 126*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 106*x^20 + 93*x^19 + 28*x^18 + 59*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 71*x^11 + 108*x^10 + 81*x^9 + 18*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 22*x^4 + 123*x^3 + 116*x^2 + 77*x + 82, x^95 + 15*x^93 + 50*x^92 + 69*x^91 + 20*x^90 + 99*x^89 + 22*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 50*x^84 + 57*x^83 + 76*x^82 + 63*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 35*x^75 + 124*x^74 + 21*x^73 + 106*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 94*x^68 + 7*x^67 + 100*x^66 + 33*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 57*x^27 + 36*x^26 + 15*x^25 + 110*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 58*x^20 + 93*x^19 + 60*x^18 + 123*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 71*x^11 + 12*x^10 + 17*x^9 + 34*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 70*x^4 + 123*x^3 + 84*x^2 + 13*x + 98, x^95 + 15*x^93 + 38*x^92 + 85*x^91 + 124*x^90 + 51*x^89 + 50*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 38*x^84 + 105*x^83 + 36*x^82 + 47*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 83*x^75 + 52*x^74 + 5*x^73 + 78*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 10*x^68 + 23*x^67 + 108*x^66 + 113*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 9*x^27 + 44*x^26 + 31*x^25 + 122*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 126*x^20 + 77*x^19 + 116*x^18 + 43*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 55*x^11 + 100*x^10 + 65*x^9 + 54*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 2*x^4 + 75*x^3 + 60*x^2 + 29*x + 118, x^95 + 15*x^93 + 26*x^92 + 21*x^91 + 4*x^90 + 115*x^89 + 14*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 26*x^84 + 41*x^83 + 92*x^82 + 111*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 70*x^76 + 19*x^75 + 76*x^74 + 69*x^73 + 114*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 54*x^68 + 87*x^67 + 20*x^66 + 49*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 73*x^27 + 84*x^26 + 95*x^25 + 70*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 66*x^20 + 13*x^19 + 12*x^18 + 107*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 78*x^12 + 119*x^11 + 28*x^10 + x^9 + 10*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 62*x^4 + 11*x^3 + 68*x^2 + 93*x + 74, x^95 + 15*x^93 + 90*x^92 + 85*x^91 + 4*x^90 + 115*x^89 + 14*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 90*x^84 + 105*x^83 + 92*x^82 + 111*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 83*x^75 + 76*x^74 + 69*x^73 + 114*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 118*x^68 + 23*x^67 + 20*x^66 + 49*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 9*x^27 + 84*x^26 + 95*x^25 + 70*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 2*x^20 + 77*x^19 + 12*x^18 + 107*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 55*x^11 + 28*x^10 + x^9 + 10*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 126*x^4 + 75*x^3 + 68*x^2 + 93*x + 74, x^95 + 15*x^93 + 62*x^92 + 117*x^91 + 124*x^90 + 115*x^89 + 10*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 30*x^84 + 73*x^83 + 100*x^82 + 111*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 51*x^75 + 52*x^74 + 69*x^73 + 54*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 18*x^68 + 55*x^67 + 44*x^66 + 49*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 41*x^27 + 44*x^26 + 95*x^25 + 50*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 86*x^20 + 45*x^19 + 52*x^18 + 107*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 23*x^11 + 100*x^10 + x^9 + 126*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 106*x^4 + 107*x^3 + 124*x^2 + 93*x + 30, x^95 + 15*x^93 + 90*x^92 + 117*x^91 + 100*x^90 + 83*x^89 + 46*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 26*x^84 + 73*x^83 + 124*x^82 + 15*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 51*x^75 + 108*x^74 + 101*x^73 + 82*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 54*x^68 + 55*x^67 + 116*x^66 + 17*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 41*x^27 + 52*x^26 + 63*x^25 + 102*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 66*x^20 + 45*x^19 + 44*x^18 + 11*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 23*x^11 + 60*x^10 + 33*x^9 + 106*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 62*x^4 + 107*x^3 + 36*x^2 + 61*x + 106, x^95 + 15*x^93 + 54*x^92 + 101*x^91 + 108*x^90 + 99*x^89 + 18*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 86*x^84 + 25*x^83 + 116*x^82 + 63*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 3*x^75 + 4*x^74 + 21*x^73 + 46*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 26*x^68 + 39*x^67 + 92*x^66 + 33*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 89*x^27 + 92*x^26 + 15*x^25 + 90*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 110*x^20 + 61*x^19 + 4*x^18 + 123*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 39*x^11 + 116*x^10 + 17*x^9 + 22*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 82*x^4 + 27*x^3 + 108*x^2 + 13*x + 118, x^95 + 15*x^93 + 94*x^92 + 5*x^91 + 12*x^90 + 35*x^89 + 26*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 94*x^84 + 121*x^83 + 20*x^82 + 127*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 99*x^75 + 100*x^74 + 85*x^73 + 102*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 18*x^68 + 71*x^67 + 60*x^66 + 97*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 121*x^27 + 124*x^26 + 79*x^25 + 2*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 22*x^20 + 29*x^19 + 36*x^18 + 59*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 7*x^11 + 84*x^10 + 81*x^9 + 110*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 106*x^4 + 59*x^3 + 76*x^2 + 77*x + 46, x^95 + 15*x^93 + 78*x^92 + 101*x^91 + 76*x^90 + 3*x^89 + 74*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 14*x^84 + 25*x^83 + 84*x^82 + 31*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 3*x^75 + 36*x^74 + 117*x^73 + 54*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 98*x^68 + 39*x^67 + 124*x^66 + 65*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 89*x^27 + 60*x^26 + 47*x^25 + 114*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 6*x^20 + 61*x^19 + 100*x^18 + 91*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 39*x^11 + 20*x^10 + 113*x^9 + 126*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 122*x^4 + 27*x^3 + 12*x^2 + 45*x + 126, x^95 + 15*x^93 + 106*x^92 + 69*x^91 + 116*x^90 + 67*x^89 + 110*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 10*x^84 + 57*x^83 + 44*x^82 + 95*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 35*x^75 + 28*x^74 + 53*x^73 + 82*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 6*x^68 + 7*x^67 + 4*x^66 + x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 57*x^27 + 4*x^26 + 111*x^25 + 38*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 114*x^20 + 93*x^19 + 28*x^18 + 27*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 71*x^11 + 44*x^10 + 49*x^9 + 106*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 78*x^4 + 123*x^3 + 116*x^2 + 109*x + 74, x^95 + 15*x^93 + 50*x^92 + 37*x^91 + 116*x^90 + 67*x^89 + 118*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 114*x^84 + 89*x^83 + 108*x^82 + 95*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 67*x^75 + 28*x^74 + 53*x^73 + 10*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 30*x^68 + 103*x^67 + 68*x^66 + x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 25*x^27 + 4*x^26 + 111*x^25 + 78*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 122*x^20 + 125*x^19 + 92*x^18 + 27*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 103*x^11 + 44*x^10 + 49*x^9 + 66*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 6*x^4 + 91*x^3 + 52*x^2 + 109*x + 66, x^95 + 15*x^93 + 118*x^92 + 5*x^91 + 44*x^90 + 3*x^89 + 82*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 22*x^84 + 121*x^83 + 52*x^82 + 31*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 99*x^75 + 68*x^74 + 117*x^73 + 110*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 90*x^68 + 71*x^67 + 28*x^66 + 65*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 121*x^27 + 28*x^26 + 47*x^25 + 26*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 46*x^20 + 29*x^19 + 68*x^18 + 91*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 7*x^11 + 52*x^10 + 113*x^9 + 86*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 18*x^4 + 59*x^3 + 44*x^2 + 45*x + 54, x^95 + 15*x^93 + 126*x^92 + 21*x^91 + 124*x^90 + 19*x^89 + 10*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 94*x^84 + 41*x^83 + 100*x^82 + 79*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 19*x^75 + 52*x^74 + 37*x^73 + 54*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 82*x^68 + 87*x^67 + 44*x^66 + 81*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 73*x^27 + 44*x^26 + 127*x^25 + 50*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 22*x^20 + 13*x^19 + 52*x^18 + 75*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 119*x^11 + 100*x^10 + 97*x^9 + 126*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 42*x^4 + 11*x^3 + 124*x^2 + 125*x + 30, x^95 + 15*x^93 + 114*x^92 + 37*x^91 + 116*x^90 + 67*x^89 + 54*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 50*x^84 + 89*x^83 + 108*x^82 + 95*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 67*x^75 + 28*x^74 + 53*x^73 + 74*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 94*x^68 + 103*x^67 + 68*x^66 + x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 25*x^27 + 4*x^26 + 111*x^25 + 14*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 58*x^20 + 125*x^19 + 92*x^18 + 27*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 103*x^11 + 44*x^10 + 49*x^9 + 2*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 70*x^4 + 91*x^3 + 52*x^2 + 109*x + 2, x^95 + 15*x^93 + 114*x^92 + 5*x^91 + 116*x^90 + 99*x^89 + 54*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 50*x^84 + 121*x^83 + 108*x^82 + 63*x^81 + 6*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 99*x^75 + 28*x^74 + 21*x^73 + 74*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 94*x^68 + 71*x^67 + 68*x^66 + 33*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 121*x^27 + 4*x^26 + 15*x^25 + 14*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 58*x^20 + 29*x^19 + 92*x^18 + 123*x^17 + 94*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 7*x^11 + 44*x^10 + 17*x^9 + 2*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 70*x^4 + 59*x^3 + 52*x^2 + 13*x + 2, x^95 + 15*x^93 + 38*x^92 + 53*x^91 + 60*x^90 + 83*x^89 + 114*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 38*x^84 + 9*x^83 + 100*x^82 + 15*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 115*x^75 + 116*x^74 + 101*x^73 + 14*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 10*x^68 + 119*x^67 + 44*x^66 + 17*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 105*x^27 + 108*x^26 + 63*x^25 + 58*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 126*x^20 + 109*x^19 + 52*x^18 + 11*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 87*x^11 + 36*x^10 + 33*x^9 + 118*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 2*x^4 + 43*x^3 + 124*x^2 + 61*x + 54, x^95 + 15*x^93 + 94*x^92 + 85*x^91 + 28*x^90 + 19*x^89 + 10*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 126*x^84 + 105*x^83 + 68*x^82 + 79*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 83*x^75 + 20*x^74 + 37*x^73 + 54*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 50*x^68 + 23*x^67 + 76*x^66 + 81*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 9*x^27 + 76*x^26 + 127*x^25 + 50*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 54*x^20 + 77*x^19 + 20*x^18 + 75*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 55*x^11 + 68*x^10 + 97*x^9 + 126*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 10*x^4 + 75*x^3 + 28*x^2 + 125*x + 94, x^95 + 15*x^93 + 42*x^92 + 21*x^91 + 4*x^90 + 115*x^89 + 94*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 106*x^84 + 41*x^83 + 92*x^82 + 111*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 19*x^75 + 76*x^74 + 69*x^73 + 34*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 102*x^68 + 87*x^67 + 20*x^66 + 49*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 73*x^27 + 84*x^26 + 95*x^25 + 86*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 82*x^20 + 13*x^19 + 12*x^18 + 107*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 119*x^11 + 28*x^10 + x^9 + 122*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 46*x^4 + 11*x^3 + 68*x^2 + 93*x + 122, x^95 + 15*x^93 + 22*x^92 + 117*x^91 + 60*x^90 + 19*x^89 + 34*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 86*x^84 + 73*x^83 + 100*x^82 + 79*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 51*x^75 + 116*x^74 + 37*x^73 + 94*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 90*x^68 + 55*x^67 + 44*x^66 + 81*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 41*x^27 + 108*x^26 + 127*x^25 + 42*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 110*x^20 + 45*x^19 + 52*x^18 + 75*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 23*x^11 + 36*x^10 + 97*x^9 + 6*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 18*x^4 + 107*x^3 + 124*x^2 + 125*x + 6, x^95 + 15*x^93 + 98*x^92 + 37*x^91 + 116*x^90 + 67*x^89 + 102*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 98*x^84 + 89*x^83 + 108*x^82 + 95*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 67*x^75 + 28*x^74 + 53*x^73 + 26*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 46*x^68 + 103*x^67 + 68*x^66 + x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 25*x^27 + 4*x^26 + 111*x^25 + 126*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 42*x^20 + 125*x^19 + 92*x^18 + 27*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 103*x^11 + 44*x^10 + 49*x^9 + 18*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 86*x^4 + 91*x^3 + 52*x^2 + 109*x + 82, x^95 + 15*x^93 + 62*x^92 + 37*x^91 + 12*x^90 + 67*x^89 + 58*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 62*x^84 + 89*x^83 + 20*x^82 + 95*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 67*x^75 + 100*x^74 + 53*x^73 + 70*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 50*x^68 + 103*x^67 + 60*x^66 + x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 25*x^27 + 124*x^26 + 111*x^25 + 34*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 118*x^20 + 125*x^19 + 36*x^18 + 27*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 103*x^11 + 84*x^10 + 49*x^9 + 78*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 10*x^4 + 91*x^3 + 76*x^2 + 109*x + 14, x^95 + 15*x^93 + 50*x^92 + 117*x^91 + 36*x^90 + 115*x^89 + 6*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 82*x^84 + 73*x^83 + 124*x^82 + 111*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 51*x^75 + 44*x^74 + 69*x^73 + 58*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 126*x^68 + 55*x^67 + 116*x^66 + 49*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 41*x^27 + 116*x^26 + 95*x^25 + 30*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 90*x^20 + 45*x^19 + 44*x^18 + 107*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 23*x^11 + 124*x^10 + x^9 + 50*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 102*x^4 + 107*x^3 + 36*x^2 + 93*x + 18, x^95 + 15*x^93 + 10*x^92 + 117*x^91 + 4*x^90 + 83*x^89 + 126*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 74*x^84 + 73*x^83 + 92*x^82 + 15*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 51*x^75 + 76*x^74 + 101*x^73 + 2*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 6*x^68 + 55*x^67 + 20*x^66 + 17*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 41*x^27 + 84*x^26 + 63*x^25 + 118*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 50*x^20 + 45*x^19 + 12*x^18 + 11*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 23*x^11 + 28*x^10 + 33*x^9 + 90*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 78*x^4 + 107*x^3 + 68*x^2 + 61*x + 90, x^95 + 15*x^93 + 42*x^92 + 117*x^91 + 100*x^90 + 19*x^89 + 126*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 42*x^84 + 73*x^83 + 124*x^82 + 79*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 51*x^75 + 108*x^74 + 37*x^73 + 2*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 38*x^68 + 55*x^67 + 116*x^66 + 81*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 41*x^27 + 52*x^26 + 127*x^25 + 118*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 18*x^20 + 45*x^19 + 44*x^18 + 75*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 23*x^11 + 60*x^10 + 97*x^9 + 90*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 110*x^4 + 107*x^3 + 36*x^2 + 125*x + 26, x^95 + 15*x^93 + 2*x^92 + 85*x^91 + 4*x^90 + 19*x^89 + 54*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 34*x^84 + 105*x^83 + 28*x^82 + 79*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 83*x^75 + 76*x^74 + 37*x^73 + 10*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 46*x^68 + 23*x^67 + 84*x^66 + 81*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 9*x^27 + 84*x^26 + 127*x^25 + 14*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 106*x^20 + 77*x^19 + 76*x^18 + 75*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 55*x^11 + 28*x^10 + 97*x^9 + 66*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 86*x^4 + 75*x^3 + 4*x^2 + 125*x + 34, x^95 + 15*x^93 + 106*x^92 + 101*x^91 + 84*x^90 + 99*x^89 + 78*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 74*x^84 + 25*x^83 + 76*x^82 + 63*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 3*x^75 + 60*x^74 + 21*x^73 + 114*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 70*x^68 + 39*x^67 + 100*x^66 + 33*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 89*x^27 + 100*x^26 + 15*x^25 + 6*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 50*x^20 + 61*x^19 + 60*x^18 + 123*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 39*x^11 + 76*x^10 + 17*x^9 + 10*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 14*x^4 + 27*x^3 + 84*x^2 + 13*x + 42, x^95 + 15*x^93 + 50*x^92 + 117*x^91 + 68*x^90 + 51*x^89 + 38*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 18*x^84 + 73*x^83 + 92*x^82 + 47*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 51*x^75 + 12*x^74 + 5*x^73 + 26*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 62*x^68 + 55*x^67 + 20*x^66 + 113*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 41*x^27 + 20*x^26 + 31*x^25 + 62*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 26*x^20 + 45*x^19 + 12*x^18 + 43*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 23*x^11 + 92*x^10 + 65*x^9 + 18*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 38*x^4 + 107*x^3 + 68*x^2 + 29*x + 50, x^95 + 15*x^93 + 42*x^92 + 117*x^91 + 4*x^90 + 83*x^89 + 30*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 106*x^84 + 73*x^83 + 92*x^82 + 15*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 51*x^75 + 76*x^74 + 101*x^73 + 98*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 102*x^68 + 55*x^67 + 20*x^66 + 17*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 41*x^27 + 84*x^26 + 63*x^25 + 22*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 82*x^20 + 45*x^19 + 12*x^18 + 11*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 23*x^11 + 28*x^10 + 33*x^9 + 58*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 46*x^4 + 107*x^3 + 68*x^2 + 61*x + 58, x^95 + 15*x^93 + 66*x^92 + 69*x^91 + 20*x^90 + 99*x^89 + 102*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 2*x^84 + 57*x^83 + 76*x^82 + 63*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 35*x^75 + 124*x^74 + 21*x^73 + 26*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 14*x^68 + 7*x^67 + 100*x^66 + 33*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 57*x^27 + 36*x^26 + 15*x^25 + 126*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 74*x^20 + 93*x^19 + 60*x^18 + 123*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 71*x^11 + 12*x^10 + 17*x^9 + 18*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 54*x^4 + 123*x^3 + 84*x^2 + 13*x + 18, x^95 + 15*x^93 + 54*x^92 + 21*x^91 + 124*x^90 + 51*x^89 + 66*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 118*x^84 + 41*x^83 + 36*x^82 + 47*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 19*x^75 + 52*x^74 + 5*x^73 + 62*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 58*x^68 + 87*x^67 + 108*x^66 + 113*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 73*x^27 + 44*x^26 + 31*x^25 + 74*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 14*x^20 + 13*x^19 + 116*x^18 + 43*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 119*x^11 + 100*x^10 + 65*x^9 + 102*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 114*x^4 + 11*x^3 + 60*x^2 + 29*x + 102, x^95 + 15*x^93 + 126*x^92 + 53*x^91 + 92*x^90 + 115*x^89 + 42*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 30*x^84 + 9*x^83 + 4*x^82 + 111*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 115*x^75 + 84*x^74 + 69*x^73 + 22*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 18*x^68 + 119*x^67 + 12*x^66 + 49*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 105*x^27 + 12*x^26 + 95*x^25 + 82*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 86*x^20 + 109*x^19 + 84*x^18 + 107*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 87*x^11 + 4*x^10 + x^9 + 94*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 106*x^4 + 43*x^3 + 92*x^2 + 93*x + 62, x^95 + 15*x^93 + 46*x^92 + 69*x^91 + 76*x^90 + 35*x^89 + 42*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 110*x^84 + 57*x^83 + 84*x^82 + 127*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 35*x^75 + 36*x^74 + 85*x^73 + 86*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 2*x^68 + 7*x^67 + 124*x^66 + 97*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 57*x^27 + 60*x^26 + 79*x^25 + 82*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 102*x^20 + 93*x^19 + 100*x^18 + 59*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 71*x^11 + 20*x^10 + 81*x^9 + 30*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 26*x^4 + 123*x^3 + 12*x^2 + 77*x + 30, x^95 + 15*x^93 + 34*x^92 + 5*x^91 + 20*x^90 + 35*x^89 + 70*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 98*x^84 + 121*x^83 + 76*x^82 + 127*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 99*x^75 + 124*x^74 + 85*x^73 + 58*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 46*x^68 + 71*x^67 + 100*x^66 + 97*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 121*x^27 + 36*x^26 + 79*x^25 + 94*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 42*x^20 + 29*x^19 + 60*x^18 + 59*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 7*x^11 + 12*x^10 + 81*x^9 + 50*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 86*x^4 + 59*x^3 + 84*x^2 + 77*x + 50, x^95 + 15*x^93 + 34*x^92 + 37*x^91 + 84*x^90 + 3*x^89 + 6*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 98*x^84 + 89*x^83 + 12*x^82 + 31*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 67*x^75 + 60*x^74 + 117*x^73 + 122*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 46*x^68 + 103*x^67 + 36*x^66 + 65*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 25*x^27 + 100*x^26 + 47*x^25 + 30*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 42*x^20 + 125*x^19 + 124*x^18 + 91*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 103*x^11 + 76*x^10 + 113*x^9 + 114*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 86*x^4 + 91*x^3 + 20*x^2 + 45*x + 114, x^95 + 15*x^93 + 86*x^92 + 69*x^91 + 12*x^90 + 3*x^89 + 18*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 54*x^84 + 57*x^83 + 84*x^82 + 31*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 35*x^75 + 100*x^74 + 117*x^73 + 46*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 58*x^68 + 7*x^67 + 124*x^66 + 65*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 57*x^27 + 124*x^26 + 47*x^25 + 90*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 78*x^20 + 93*x^19 + 100*x^18 + 91*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 71*x^11 + 84*x^10 + 113*x^9 + 22*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 114*x^4 + 123*x^3 + 12*x^2 + 45*x + 54, x^95 + 15*x^93 + 2*x^92 + 5*x^91 + 20*x^90 + 35*x^89 + 38*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 66*x^84 + 121*x^83 + 76*x^82 + 127*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 99*x^75 + 124*x^74 + 85*x^73 + 90*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 78*x^68 + 71*x^67 + 100*x^66 + 97*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 121*x^27 + 36*x^26 + 79*x^25 + 62*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 10*x^20 + 29*x^19 + 60*x^18 + 59*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 7*x^11 + 12*x^10 + 81*x^9 + 82*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 118*x^4 + 59*x^3 + 84*x^2 + 77*x + 82, x^95 + 15*x^93 + 54*x^92 + 53*x^91 + 28*x^90 + 19*x^89 + 34*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 54*x^84 + 9*x^83 + 4*x^82 + 79*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 115*x^75 + 20*x^74 + 37*x^73 + 94*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 122*x^68 + 119*x^67 + 12*x^66 + 81*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 105*x^27 + 76*x^26 + 127*x^25 + 42*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 78*x^20 + 109*x^19 + 84*x^18 + 75*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 87*x^11 + 68*x^10 + 97*x^9 + 6*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 50*x^4 + 43*x^3 + 92*x^2 + 125*x + 70, x^95 + 15*x^93 + 66*x^92 + 69*x^91 + 52*x^90 + 35*x^89 + 6*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 66*x^84 + 57*x^83 + 44*x^82 + 127*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 35*x^75 + 92*x^74 + 85*x^73 + 122*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 78*x^68 + 7*x^67 + 4*x^66 + 97*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 57*x^27 + 68*x^26 + 79*x^25 + 30*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 10*x^20 + 93*x^19 + 28*x^18 + 59*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 71*x^11 + 108*x^10 + 81*x^9 + 114*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 118*x^4 + 123*x^3 + 116*x^2 + 77*x + 50, x^95 + 15*x^93 + 14*x^92 + 53*x^91 + 60*x^90 + 115*x^89 + 26*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 46*x^84 + 9*x^83 + 36*x^82 + 111*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 115*x^75 + 116*x^74 + 69*x^73 + 38*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 2*x^68 + 119*x^67 + 108*x^66 + 49*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 105*x^27 + 108*x^26 + 95*x^25 + 2*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 38*x^20 + 109*x^19 + 116*x^18 + 107*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 87*x^11 + 36*x^10 + x^9 + 46*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 26*x^4 + 43*x^3 + 60*x^2 + 93*x + 14, x^95 + 15*x^93 + 114*x^92 + 85*x^91 + 68*x^90 + 83*x^89 + 102*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 82*x^84 + 105*x^83 + 92*x^82 + 15*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 83*x^75 + 12*x^74 + 101*x^73 + 90*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 126*x^68 + 23*x^67 + 20*x^66 + 17*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 9*x^27 + 20*x^26 + 63*x^25 + 126*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 90*x^20 + 77*x^19 + 12*x^18 + 11*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 55*x^11 + 92*x^10 + 33*x^9 + 82*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 102*x^4 + 75*x^3 + 68*x^2 + 61*x + 114, x^95 + 15*x^93 + 74*x^92 + 101*x^91 + 20*x^90 + 99*x^89 + 110*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 42*x^84 + 25*x^83 + 12*x^82 + 63*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 3*x^75 + 124*x^74 + 21*x^73 + 82*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 102*x^68 + 39*x^67 + 36*x^66 + 33*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 89*x^27 + 36*x^26 + 15*x^25 + 38*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 18*x^20 + 61*x^19 + 124*x^18 + 123*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 39*x^11 + 12*x^10 + 17*x^9 + 106*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 46*x^4 + 27*x^3 + 20*x^2 + 13*x + 10, x^95 + 15*x^93 + 14*x^92 + 5*x^91 + 44*x^90 + 99*x^89 + 42*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 14*x^84 + 121*x^83 + 116*x^82 + 63*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 99*x^75 + 68*x^74 + 21*x^73 + 86*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 98*x^68 + 71*x^67 + 92*x^66 + 33*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 121*x^27 + 28*x^26 + 15*x^25 + 82*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 6*x^20 + 29*x^19 + 4*x^18 + 123*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 7*x^11 + 52*x^10 + 17*x^9 + 30*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 122*x^4 + 59*x^3 + 108*x^2 + 13*x + 94, x^95 + 15*x^93 + 126*x^92 + 5*x^91 + 108*x^90 + 99*x^89 + 26*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 62*x^84 + 121*x^83 + 52*x^82 + 63*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 99*x^75 + 4*x^74 + 21*x^73 + 102*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 50*x^68 + 71*x^67 + 28*x^66 + 33*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 121*x^27 + 92*x^26 + 15*x^25 + 2*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 118*x^20 + 29*x^19 + 68*x^18 + 123*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 7*x^11 + 116*x^10 + 17*x^9 + 110*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 10*x^4 + 59*x^3 + 44*x^2 + 13*x + 110, x^95 + 15*x^93 + 126*x^92 + 5*x^91 + 12*x^90 + 35*x^89 + 58*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 126*x^84 + 121*x^83 + 20*x^82 + 127*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 99*x^75 + 100*x^74 + 85*x^73 + 70*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 114*x^68 + 71*x^67 + 60*x^66 + 97*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 121*x^27 + 124*x^26 + 79*x^25 + 34*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 54*x^20 + 29*x^19 + 36*x^18 + 59*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 7*x^11 + 84*x^10 + 81*x^9 + 78*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 74*x^4 + 59*x^3 + 76*x^2 + 77*x + 14, x^95 + 15*x^93 + 114*x^92 + 117*x^91 + 100*x^90 + 51*x^89 + 70*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 18*x^84 + 73*x^83 + 60*x^82 + 47*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 51*x^75 + 108*x^74 + 5*x^73 + 122*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 62*x^68 + 55*x^67 + 52*x^66 + 113*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 41*x^27 + 52*x^26 + 31*x^25 + 94*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 26*x^20 + 45*x^19 + 108*x^18 + 43*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 23*x^11 + 60*x^10 + 65*x^9 + 114*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 38*x^4 + 107*x^3 + 100*x^2 + 29*x + 82, x^95 + 15*x^93 + 14*x^92 + 21*x^91 + 28*x^90 + 19*x^89 + 58*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 110*x^84 + 41*x^83 + 68*x^82 + 79*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 19*x^75 + 20*x^74 + 37*x^73 + 6*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 66*x^68 + 87*x^67 + 76*x^66 + 81*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 73*x^27 + 76*x^26 + 127*x^25 + 34*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 102*x^20 + 13*x^19 + 20*x^18 + 75*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 119*x^11 + 68*x^10 + 97*x^9 + 14*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 90*x^4 + 11*x^3 + 28*x^2 + 125*x + 46, x^95 + 15*x^93 + 122*x^92 + 117*x^91 + 4*x^90 + 19*x^89 + 110*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 122*x^84 + 73*x^83 + 92*x^82 + 79*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 51*x^75 + 76*x^74 + 37*x^73 + 18*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 86*x^68 + 55*x^67 + 20*x^66 + 81*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 41*x^27 + 84*x^26 + 127*x^25 + 38*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 34*x^20 + 45*x^19 + 12*x^18 + 75*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 23*x^11 + 28*x^10 + 97*x^9 + 42*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 94*x^4 + 107*x^3 + 68*x^2 + 125*x + 106, x^95 + 15*x^93 + 66*x^92 + 69*x^91 + 20*x^90 + 35*x^89 + 38*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 2*x^84 + 57*x^83 + 76*x^82 + 127*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 35*x^75 + 124*x^74 + 85*x^73 + 90*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 14*x^68 + 7*x^67 + 100*x^66 + 97*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 57*x^27 + 36*x^26 + 79*x^25 + 62*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 74*x^20 + 93*x^19 + 60*x^18 + 59*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 71*x^11 + 12*x^10 + 81*x^9 + 82*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 54*x^4 + 123*x^3 + 84*x^2 + 77*x + 82, x^95 + 15*x^93 + 78*x^92 + 69*x^91 + 76*x^90 + 35*x^89 + 74*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 14*x^84 + 57*x^83 + 84*x^82 + 127*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 35*x^75 + 36*x^74 + 85*x^73 + 54*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 98*x^68 + 7*x^67 + 124*x^66 + 97*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 57*x^27 + 60*x^26 + 79*x^25 + 114*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 6*x^20 + 93*x^19 + 100*x^18 + 59*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 71*x^11 + 20*x^10 + 81*x^9 + 126*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 122*x^4 + 123*x^3 + 12*x^2 + 77*x + 126, x^95 + 15*x^93 + 110*x^92 + 37*x^91 + 108*x^90 + 67*x^89 + 74*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 110*x^84 + 89*x^83 + 52*x^82 + 95*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 67*x^75 + 4*x^74 + 53*x^73 + 54*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 2*x^68 + 103*x^67 + 28*x^66 + x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 25*x^27 + 92*x^26 + 111*x^25 + 114*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 102*x^20 + 125*x^19 + 68*x^18 + 27*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 103*x^11 + 116*x^10 + 49*x^9 + 126*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 26*x^4 + 91*x^3 + 44*x^2 + 109*x + 62, x^95 + 15*x^93 + 94*x^92 + 53*x^91 + 92*x^90 + 51*x^89 + 74*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 126*x^84 + 9*x^83 + 4*x^82 + 47*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 115*x^75 + 84*x^74 + 5*x^73 + 118*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 50*x^68 + 119*x^67 + 12*x^66 + 113*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 105*x^27 + 12*x^26 + 31*x^25 + 114*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 54*x^20 + 109*x^19 + 84*x^18 + 43*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 87*x^11 + 4*x^10 + 65*x^9 + 62*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 10*x^4 + 43*x^3 + 92*x^2 + 29*x + 30, x^95 + 15*x^93 + 118*x^92 + 85*x^91 + 60*x^90 + 115*x^89 + 66*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 54*x^84 + 105*x^83 + 100*x^82 + 111*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 83*x^75 + 116*x^74 + 69*x^73 + 62*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 122*x^68 + 23*x^67 + 44*x^66 + 49*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 9*x^27 + 108*x^26 + 95*x^25 + 74*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 78*x^20 + 77*x^19 + 52*x^18 + 107*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 55*x^11 + 36*x^10 + x^9 + 102*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 50*x^4 + 75*x^3 + 124*x^2 + 93*x + 102, x^95 + 15*x^93 + 110*x^92 + 69*x^91 + 76*x^90 + 35*x^89 + 106*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 46*x^84 + 57*x^83 + 84*x^82 + 127*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 35*x^75 + 36*x^74 + 85*x^73 + 22*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 66*x^68 + 7*x^67 + 124*x^66 + 97*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 57*x^27 + 60*x^26 + 79*x^25 + 18*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 38*x^20 + 93*x^19 + 100*x^18 + 59*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 71*x^11 + 20*x^10 + 81*x^9 + 94*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 90*x^4 + 123*x^3 + 12*x^2 + 77*x + 94, x^95 + 15*x^93 + 50*x^92 + 101*x^91 + 20*x^90 + 3*x^89 + 86*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 50*x^84 + 25*x^83 + 76*x^82 + 31*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 3*x^75 + 124*x^74 + 117*x^73 + 42*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 94*x^68 + 39*x^67 + 100*x^66 + 65*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 89*x^27 + 36*x^26 + 47*x^25 + 46*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 58*x^20 + 61*x^19 + 60*x^18 + 91*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 39*x^11 + 12*x^10 + 113*x^9 + 98*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 70*x^4 + 27*x^3 + 84*x^2 + 45*x + 34, x^95 + 15*x^93 + 62*x^92 + 5*x^91 + 108*x^90 + 35*x^89 + 26*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 126*x^84 + 121*x^83 + 52*x^82 + 127*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 99*x^75 + 4*x^74 + 85*x^73 + 102*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 114*x^68 + 71*x^67 + 28*x^66 + 97*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 121*x^27 + 92*x^26 + 79*x^25 + 2*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 54*x^20 + 29*x^19 + 68*x^18 + 59*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 7*x^11 + 116*x^10 + 81*x^9 + 110*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 74*x^4 + 59*x^3 + 44*x^2 + 77*x + 110, x^95 + 15*x^93 + 86*x^92 + 117*x^91 + 60*x^90 + 83*x^89 + 34*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 22*x^84 + 73*x^83 + 100*x^82 + 15*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 51*x^75 + 116*x^74 + 101*x^73 + 94*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 26*x^68 + 55*x^67 + 44*x^66 + 17*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 41*x^27 + 108*x^26 + 63*x^25 + 42*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 46*x^20 + 45*x^19 + 52*x^18 + 11*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 23*x^11 + 36*x^10 + 33*x^9 + 6*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 82*x^4 + 107*x^3 + 124*x^2 + 61*x + 6, x^95 + 15*x^93 + 30*x^92 + 101*x^91 + 44*x^90 + 3*x^89 + 122*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 94*x^84 + 25*x^83 + 116*x^82 + 31*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 3*x^75 + 68*x^74 + 117*x^73 + 6*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 18*x^68 + 39*x^67 + 92*x^66 + 65*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 89*x^27 + 28*x^26 + 47*x^25 + 98*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 22*x^20 + 61*x^19 + 4*x^18 + 91*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 39*x^11 + 52*x^10 + 113*x^9 + 14*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 106*x^4 + 27*x^3 + 108*x^2 + 45*x + 14, x^95 + 15*x^93 + 66*x^92 + 117*x^91 + 4*x^90 + 115*x^89 + 118*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 98*x^84 + 73*x^83 + 28*x^82 + 111*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 51*x^75 + 76*x^74 + 69*x^73 + 74*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 110*x^68 + 55*x^67 + 84*x^66 + 49*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 41*x^27 + 84*x^26 + 95*x^25 + 78*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 42*x^20 + 45*x^19 + 76*x^18 + 107*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 23*x^11 + 28*x^10 + x^9 + 2*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 22*x^4 + 107*x^3 + 4*x^2 + 93*x + 98, x^95 + 15*x^93 + 118*x^92 + 37*x^91 + 108*x^90 + 35*x^89 + 82*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 22*x^84 + 89*x^83 + 116*x^82 + 127*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 67*x^75 + 4*x^74 + 85*x^73 + 110*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 90*x^68 + 103*x^67 + 92*x^66 + 97*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 25*x^27 + 92*x^26 + 79*x^25 + 26*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 46*x^20 + 125*x^19 + 4*x^18 + 59*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 103*x^11 + 116*x^10 + 81*x^9 + 86*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 18*x^4 + 91*x^3 + 108*x^2 + 77*x + 54, x^95 + 15*x^93 + 114*x^92 + 21*x^91 + 68*x^90 + 19*x^89 + 102*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 82*x^84 + 41*x^83 + 92*x^82 + 79*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 19*x^75 + 12*x^74 + 37*x^73 + 90*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 126*x^68 + 87*x^67 + 20*x^66 + 81*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 73*x^27 + 20*x^26 + 127*x^25 + 126*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 90*x^20 + 13*x^19 + 12*x^18 + 75*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 119*x^11 + 92*x^10 + 97*x^9 + 82*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 102*x^4 + 11*x^3 + 68*x^2 + 125*x + 114, x^95 + 15*x^93 + 126*x^92 + 101*x^91 + 108*x^90 + 3*x^89 + 26*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 62*x^84 + 25*x^83 + 52*x^82 + 31*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 3*x^75 + 4*x^74 + 117*x^73 + 102*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 50*x^68 + 39*x^67 + 28*x^66 + 65*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 89*x^27 + 92*x^26 + 47*x^25 + 2*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 118*x^20 + 61*x^19 + 68*x^18 + 91*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 39*x^11 + 116*x^10 + 113*x^9 + 110*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 10*x^4 + 27*x^3 + 44*x^2 + 45*x + 110, x^95 + 15*x^93 + 94*x^92 + 5*x^91 + 108*x^90 + 35*x^89 + 58*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 30*x^84 + 121*x^83 + 52*x^82 + 127*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 99*x^75 + 4*x^74 + 85*x^73 + 70*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 82*x^68 + 71*x^67 + 28*x^66 + 97*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 121*x^27 + 92*x^26 + 79*x^25 + 34*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 86*x^20 + 29*x^19 + 68*x^18 + 59*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 7*x^11 + 116*x^10 + 81*x^9 + 78*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 42*x^4 + 59*x^3 + 44*x^2 + 77*x + 78, x^95 + 15*x^93 + 94*x^92 + 69*x^91 + 108*x^90 + 99*x^89 + 58*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 30*x^84 + 57*x^83 + 52*x^82 + 63*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 35*x^75 + 4*x^74 + 21*x^73 + 70*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 82*x^68 + 7*x^67 + 28*x^66 + 33*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 57*x^27 + 92*x^26 + 15*x^25 + 34*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 86*x^20 + 93*x^19 + 68*x^18 + 123*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 71*x^11 + 116*x^10 + 17*x^9 + 78*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 42*x^4 + 123*x^3 + 44*x^2 + 13*x + 78, x^95 + 15*x^93 + 38*x^92 + 85*x^91 + 124*x^90 + 115*x^89 + 114*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 38*x^84 + 105*x^83 + 36*x^82 + 111*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 83*x^75 + 52*x^74 + 69*x^73 + 14*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 10*x^68 + 23*x^67 + 108*x^66 + 49*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 9*x^27 + 44*x^26 + 95*x^25 + 58*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 126*x^20 + 77*x^19 + 116*x^18 + 107*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 55*x^11 + 100*x^10 + x^9 + 118*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 2*x^4 + 75*x^3 + 60*x^2 + 93*x + 54, x^95 + 15*x^93 + 94*x^92 + 85*x^91 + 28*x^90 + 83*x^89 + 74*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 126*x^84 + 105*x^83 + 68*x^82 + 15*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 83*x^75 + 20*x^74 + 101*x^73 + 118*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 50*x^68 + 23*x^67 + 76*x^66 + 17*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 9*x^27 + 76*x^26 + 63*x^25 + 114*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 54*x^20 + 77*x^19 + 20*x^18 + 11*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 55*x^11 + 68*x^10 + 33*x^9 + 62*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 10*x^4 + 75*x^3 + 28*x^2 + 61*x + 30, x^95 + 15*x^93 + 90*x^92 + 53*x^91 + 100*x^90 + 19*x^89 + 46*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 26*x^84 + 9*x^83 + 124*x^82 + 79*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 115*x^75 + 108*x^74 + 37*x^73 + 82*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 54*x^68 + 119*x^67 + 116*x^66 + 81*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 105*x^27 + 52*x^26 + 127*x^25 + 102*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 66*x^20 + 109*x^19 + 44*x^18 + 75*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 87*x^11 + 60*x^10 + 97*x^9 + 106*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 62*x^4 + 43*x^3 + 36*x^2 + 125*x + 106, x^95 + 15*x^93 + 10*x^92 + 117*x^91 + 68*x^90 + 83*x^89 + 62*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 74*x^84 + 73*x^83 + 28*x^82 + 15*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 51*x^75 + 12*x^74 + 101*x^73 + 66*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 6*x^68 + 55*x^67 + 84*x^66 + 17*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 41*x^27 + 20*x^26 + 63*x^25 + 54*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 50*x^20 + 45*x^19 + 76*x^18 + 11*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 23*x^11 + 92*x^10 + 33*x^9 + 26*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 78*x^4 + 107*x^3 + 4*x^2 + 61*x + 26, x^95 + 15*x^93 + 122*x^92 + 37*x^91 + 52*x^90 + 99*x^89 + 126*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 90*x^84 + 89*x^83 + 108*x^82 + 63*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 67*x^75 + 92*x^74 + 21*x^73 + 66*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 54*x^68 + 103*x^67 + 68*x^66 + 33*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 25*x^27 + 68*x^26 + 15*x^25 + 118*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 2*x^20 + 125*x^19 + 92*x^18 + 123*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 103*x^11 + 108*x^10 + 17*x^9 + 26*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 62*x^4 + 91*x^3 + 52*x^2 + 13*x + 58, x^95 + 15*x^93 + 58*x^92 + 5*x^91 + 20*x^90 + 67*x^89 + 30*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 90*x^84 + 121*x^83 + 12*x^82 + 95*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 99*x^75 + 124*x^74 + 53*x^73 + 34*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 54*x^68 + 71*x^67 + 36*x^66 + x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 121*x^27 + 36*x^26 + 111*x^25 + 22*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 2*x^20 + 29*x^19 + 124*x^18 + 27*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 7*x^11 + 12*x^10 + 49*x^9 + 122*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 62*x^4 + 59*x^3 + 20*x^2 + 109*x + 90, x^95 + 15*x^93 + 90*x^92 + 117*x^91 + 4*x^90 + 83*x^89 + 14*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 90*x^84 + 73*x^83 + 92*x^82 + 15*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 51*x^75 + 76*x^74 + 101*x^73 + 114*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 118*x^68 + 55*x^67 + 20*x^66 + 17*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 41*x^27 + 84*x^26 + 63*x^25 + 70*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 2*x^20 + 45*x^19 + 12*x^18 + 11*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 23*x^11 + 28*x^10 + 33*x^9 + 10*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 126*x^4 + 107*x^3 + 68*x^2 + 61*x + 74, x^95 + 15*x^93 + 58*x^92 + 37*x^91 + 116*x^90 + 99*x^89 + 126*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 26*x^84 + 89*x^83 + 44*x^82 + 63*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 67*x^75 + 28*x^74 + 21*x^73 + 66*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 118*x^68 + 103*x^67 + 4*x^66 + 33*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 25*x^27 + 4*x^26 + 15*x^25 + 118*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 66*x^20 + 125*x^19 + 28*x^18 + 123*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 103*x^11 + 44*x^10 + 17*x^9 + 26*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 126*x^4 + 91*x^3 + 116*x^2 + 13*x + 58, x^95 + 15*x^93 + 118*x^92 + 37*x^91 + 12*x^90 + 99*x^89 + 114*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 86*x^84 + 89*x^83 + 84*x^82 + 63*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 67*x^75 + 100*x^74 + 21*x^73 + 78*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 26*x^68 + 103*x^67 + 124*x^66 + 33*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 25*x^27 + 124*x^26 + 15*x^25 + 58*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 110*x^20 + 125*x^19 + 100*x^18 + 123*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 103*x^11 + 84*x^10 + 17*x^9 + 54*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 82*x^4 + 91*x^3 + 12*x^2 + 13*x + 86, x^95 + 15*x^93 + 22*x^92 + 21*x^91 + 60*x^90 + 115*x^89 + 34*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 86*x^84 + 41*x^83 + 100*x^82 + 111*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 19*x^75 + 116*x^74 + 69*x^73 + 94*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 90*x^68 + 87*x^67 + 44*x^66 + 49*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 73*x^27 + 108*x^26 + 95*x^25 + 42*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 110*x^20 + 13*x^19 + 52*x^18 + 107*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 119*x^11 + 36*x^10 + x^9 + 6*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 18*x^4 + 11*x^3 + 124*x^2 + 93*x + 6, x^95 + 15*x^93 + 2*x^92 + 101*x^91 + 20*x^90 + 67*x^89 + 38*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 66*x^84 + 25*x^83 + 76*x^82 + 95*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 3*x^75 + 124*x^74 + 53*x^73 + 90*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 78*x^68 + 39*x^67 + 100*x^66 + x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 89*x^27 + 36*x^26 + 111*x^25 + 62*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 10*x^20 + 61*x^19 + 60*x^18 + 27*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 39*x^11 + 12*x^10 + 49*x^9 + 82*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 118*x^4 + 27*x^3 + 84*x^2 + 109*x + 82, x^95 + 15*x^93 + 82*x^92 + 117*x^91 + 100*x^90 + 115*x^89 + 102*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 114*x^84 + 73*x^83 + 60*x^82 + 111*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 51*x^75 + 108*x^74 + 69*x^73 + 90*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 94*x^68 + 55*x^67 + 52*x^66 + 49*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 41*x^27 + 52*x^26 + 95*x^25 + 126*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 122*x^20 + 45*x^19 + 108*x^18 + 107*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 23*x^11 + 60*x^10 + x^9 + 82*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 70*x^4 + 107*x^3 + 100*x^2 + 93*x + 50, x^95 + 15*x^93 + 46*x^92 + 85*x^91 + 28*x^90 + 83*x^89 + 90*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 14*x^84 + 105*x^83 + 68*x^82 + 15*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 83*x^75 + 20*x^74 + 101*x^73 + 102*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 34*x^68 + 23*x^67 + 76*x^66 + 17*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 9*x^27 + 76*x^26 + 63*x^25 + 66*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 6*x^20 + 77*x^19 + 20*x^18 + 11*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 55*x^11 + 68*x^10 + 33*x^9 + 110*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 58*x^4 + 75*x^3 + 28*x^2 + 61*x + 14, x^95 + 15*x^93 + 10*x^92 + 53*x^91 + 4*x^90 + 19*x^89 + 126*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 74*x^84 + 9*x^83 + 92*x^82 + 79*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 115*x^75 + 76*x^74 + 37*x^73 + 2*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 6*x^68 + 119*x^67 + 20*x^66 + 81*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 105*x^27 + 84*x^26 + 127*x^25 + 118*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 50*x^20 + 109*x^19 + 12*x^18 + 75*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 87*x^11 + 28*x^10 + 97*x^9 + 90*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 78*x^4 + 43*x^3 + 68*x^2 + 125*x + 90, x^95 + 15*x^93 + 118*x^92 + 53*x^91 + 28*x^90 + 19*x^89 + 98*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 118*x^84 + 9*x^83 + 4*x^82 + 79*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 115*x^75 + 20*x^74 + 37*x^73 + 30*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 58*x^68 + 119*x^67 + 12*x^66 + 81*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 105*x^27 + 76*x^26 + 127*x^25 + 106*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 14*x^20 + 109*x^19 + 84*x^18 + 75*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 87*x^11 + 68*x^10 + 97*x^9 + 70*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 114*x^4 + 43*x^3 + 92*x^2 + 125*x + 6, x^95 + 15*x^93 + 82*x^92 + 117*x^91 + 4*x^90 + 115*x^89 + 70*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 50*x^84 + 73*x^83 + 28*x^82 + 111*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 51*x^75 + 76*x^74 + 69*x^73 + 122*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 30*x^68 + 55*x^67 + 84*x^66 + 49*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 41*x^27 + 84*x^26 + 95*x^25 + 94*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 58*x^20 + 45*x^19 + 76*x^18 + 107*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 23*x^11 + 28*x^10 + x^9 + 114*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 6*x^4 + 107*x^3 + 4*x^2 + 93*x + 18, x^95 + 15*x^93 + 102*x^92 + 53*x^91 + 28*x^90 + 83*x^89 + 82*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 38*x^84 + 9*x^83 + 4*x^82 + 15*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 115*x^75 + 20*x^74 + 101*x^73 + 46*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 10*x^68 + 119*x^67 + 12*x^66 + 17*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 105*x^27 + 76*x^26 + 63*x^25 + 26*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 126*x^20 + 109*x^19 + 84*x^18 + 11*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 87*x^11 + 68*x^10 + 33*x^9 + 22*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 2*x^4 + 43*x^3 + 92*x^2 + 61*x + 22, x^95 + 15*x^93 + 118*x^92 + 21*x^91 + 92*x^90 + 115*x^89 + 98*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 118*x^84 + 41*x^83 + 68*x^82 + 111*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 19*x^75 + 84*x^74 + 69*x^73 + 30*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 58*x^68 + 87*x^67 + 76*x^66 + 49*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 73*x^27 + 12*x^26 + 95*x^25 + 106*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 14*x^20 + 13*x^19 + 20*x^18 + 107*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 119*x^11 + 4*x^10 + x^9 + 70*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 114*x^4 + 11*x^3 + 28*x^2 + 93*x + 6, x^95 + 15*x^93 + 102*x^92 + 5*x^91 + 12*x^90 + 67*x^89 + 98*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 6*x^84 + 121*x^83 + 84*x^82 + 95*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 99*x^75 + 100*x^74 + 53*x^73 + 94*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 106*x^68 + 71*x^67 + 124*x^66 + x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 121*x^27 + 124*x^26 + 111*x^25 + 106*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 94*x^20 + 29*x^19 + 100*x^18 + 27*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 7*x^11 + 84*x^10 + 49*x^9 + 6*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 98*x^4 + 59*x^3 + 12*x^2 + 109*x + 102, x^95 + 15*x^93 + 106*x^92 + 85*x^91 + 36*x^90 + 115*x^89 + 62*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 106*x^84 + 105*x^83 + 60*x^82 + 111*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 83*x^75 + 44*x^74 + 69*x^73 + 66*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 102*x^68 + 23*x^67 + 52*x^66 + 49*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 9*x^27 + 116*x^26 + 95*x^25 + 54*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 82*x^20 + 77*x^19 + 108*x^18 + 107*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 55*x^11 + 124*x^10 + x^9 + 26*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 46*x^4 + 75*x^3 + 100*x^2 + 93*x + 90, x^95 + 15*x^93 + 78*x^92 + 69*x^91 + 12*x^90 + 35*x^89 + 10*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 14*x^84 + 57*x^83 + 20*x^82 + 127*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 35*x^75 + 100*x^74 + 85*x^73 + 118*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 98*x^68 + 7*x^67 + 60*x^66 + 97*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 57*x^27 + 124*x^26 + 79*x^25 + 50*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 6*x^20 + 93*x^19 + 36*x^18 + 59*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 71*x^11 + 84*x^10 + 81*x^9 + 62*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 122*x^4 + 123*x^3 + 76*x^2 + 77*x + 62, x^95 + 15*x^93 + 58*x^92 + 37*x^91 + 20*x^90 + 35*x^89 + 30*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 90*x^84 + 89*x^83 + 12*x^82 + 127*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 67*x^75 + 124*x^74 + 85*x^73 + 34*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 54*x^68 + 103*x^67 + 36*x^66 + 97*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 25*x^27 + 36*x^26 + 79*x^25 + 22*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 2*x^20 + 125*x^19 + 124*x^18 + 59*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 103*x^11 + 12*x^10 + 81*x^9 + 122*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 62*x^4 + 91*x^3 + 20*x^2 + 77*x + 90, x^95 + 15*x^93 + 106*x^92 + 69*x^91 + 84*x^90 + 3*x^89 + 78*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 74*x^84 + 57*x^83 + 76*x^82 + 31*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 35*x^75 + 60*x^74 + 117*x^73 + 114*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 70*x^68 + 7*x^67 + 100*x^66 + 65*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 57*x^27 + 100*x^26 + 47*x^25 + 6*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 50*x^20 + 93*x^19 + 60*x^18 + 91*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 71*x^11 + 76*x^10 + 113*x^9 + 10*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 14*x^4 + 123*x^3 + 84*x^2 + 45*x + 42, x^95 + 15*x^93 + 2*x^92 + 53*x^91 + 36*x^90 + 51*x^89 + 22*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 98*x^84 + 9*x^83 + 124*x^82 + 47*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 115*x^75 + 44*x^74 + 5*x^73 + 42*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 110*x^68 + 119*x^67 + 116*x^66 + 113*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 105*x^27 + 116*x^26 + 31*x^25 + 110*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 42*x^20 + 109*x^19 + 44*x^18 + 43*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 87*x^11 + 124*x^10 + 65*x^9 + 98*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 22*x^4 + 43*x^3 + 36*x^2 + 29*x + 2, x^95 + 15*x^93 + 78*x^92 + 53*x^91 + 28*x^90 + 115*x^89 + 122*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 46*x^84 + 9*x^83 + 68*x^82 + 111*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 115*x^75 + 20*x^74 + 69*x^73 + 70*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 2*x^68 + 119*x^67 + 76*x^66 + 49*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 105*x^27 + 76*x^26 + 95*x^25 + 98*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 38*x^20 + 109*x^19 + 20*x^18 + 107*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 87*x^11 + 68*x^10 + x^9 + 78*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 26*x^4 + 43*x^3 + 28*x^2 + 93*x + 110, x^95 + 15*x^93 + 102*x^92 + 85*x^91 + 60*x^90 + 115*x^89 + 114*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 102*x^84 + 105*x^83 + 100*x^82 + 111*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 83*x^75 + 116*x^74 + 69*x^73 + 14*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 74*x^68 + 23*x^67 + 44*x^66 + 49*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 9*x^27 + 108*x^26 + 95*x^25 + 58*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 62*x^20 + 77*x^19 + 52*x^18 + 107*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 55*x^11 + 36*x^10 + x^9 + 118*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 66*x^4 + 75*x^3 + 124*x^2 + 93*x + 54, x^95 + 15*x^93 + 102*x^92 + 5*x^91 + 108*x^90 + 67*x^89 + 2*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 70*x^84 + 121*x^83 + 116*x^82 + 95*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 99*x^75 + 4*x^74 + 53*x^73 + 62*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 42*x^68 + 71*x^67 + 92*x^66 + x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 121*x^27 + 92*x^26 + 111*x^25 + 10*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 30*x^20 + 29*x^19 + 4*x^18 + 27*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 7*x^11 + 116*x^10 + 49*x^9 + 102*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 34*x^4 + 59*x^3 + 108*x^2 + 109*x + 6, x^95 + 15*x^93 + 38*x^92 + 5*x^91 + 44*x^90 + 67*x^89 + 2*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 6*x^84 + 121*x^83 + 52*x^82 + 95*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 99*x^75 + 68*x^74 + 53*x^73 + 62*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 106*x^68 + 71*x^67 + 28*x^66 + x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 121*x^27 + 28*x^26 + 111*x^25 + 10*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 94*x^20 + 29*x^19 + 68*x^18 + 27*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 7*x^11 + 52*x^10 + 49*x^9 + 102*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 98*x^4 + 59*x^3 + 44*x^2 + 109*x + 6, x^95 + 15*x^93 + 70*x^92 + 37*x^91 + 12*x^90 + 35*x^89 + 66*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 102*x^84 + 89*x^83 + 84*x^82 + 127*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 67*x^75 + 100*x^74 + 85*x^73 + 126*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 10*x^68 + 103*x^67 + 124*x^66 + 97*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 25*x^27 + 124*x^26 + 79*x^25 + 74*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 62*x^20 + 125*x^19 + 100*x^18 + 59*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 103*x^11 + 84*x^10 + 81*x^9 + 38*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 2*x^4 + 91*x^3 + 12*x^2 + 77*x + 6, x^95 + 15*x^93 + 98*x^92 + 21*x^91 + 100*x^90 + 19*x^89 + 118*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 66*x^84 + 41*x^83 + 60*x^82 + 79*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 19*x^75 + 108*x^74 + 37*x^73 + 74*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 14*x^68 + 87*x^67 + 52*x^66 + 81*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 73*x^27 + 52*x^26 + 127*x^25 + 78*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 10*x^20 + 13*x^19 + 108*x^18 + 75*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 119*x^11 + 60*x^10 + 97*x^9 + 2*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 54*x^4 + 11*x^3 + 100*x^2 + 125*x + 34, x^95 + 15*x^93 + 78*x^92 + 117*x^91 + 60*x^90 + 51*x^89 + 90*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 110*x^84 + 73*x^83 + 36*x^82 + 47*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 51*x^75 + 116*x^74 + 5*x^73 + 102*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 66*x^68 + 55*x^67 + 108*x^66 + 113*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 41*x^27 + 108*x^26 + 31*x^25 + 66*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 102*x^20 + 45*x^19 + 116*x^18 + 43*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 23*x^11 + 36*x^10 + 65*x^9 + 110*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 90*x^4 + 107*x^3 + 60*x^2 + 29*x + 78, x^95 + 15*x^93 + 94*x^92 + 69*x^91 + 44*x^90 + 35*x^89 + 58*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 30*x^84 + 57*x^83 + 116*x^82 + 127*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 35*x^75 + 68*x^74 + 85*x^73 + 70*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 82*x^68 + 7*x^67 + 92*x^66 + 97*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 57*x^27 + 28*x^26 + 79*x^25 + 34*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 86*x^20 + 93*x^19 + 4*x^18 + 59*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 71*x^11 + 52*x^10 + 81*x^9 + 78*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 42*x^4 + 123*x^3 + 108*x^2 + 77*x + 78, x^95 + 15*x^93 + 74*x^92 + 21*x^91 + 100*x^90 + 115*x^89 + 30*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 74*x^84 + 41*x^83 + 124*x^82 + 111*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 19*x^75 + 108*x^74 + 69*x^73 + 98*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 6*x^68 + 87*x^67 + 116*x^66 + 49*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 73*x^27 + 52*x^26 + 95*x^25 + 22*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 50*x^20 + 13*x^19 + 44*x^18 + 107*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 119*x^11 + 60*x^10 + x^9 + 58*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 78*x^4 + 11*x^3 + 36*x^2 + 93*x + 122, x^95 + 15*x^93 + 22*x^92 + 37*x^91 + 108*x^90 + 35*x^89 + 114*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 54*x^84 + 89*x^83 + 116*x^82 + 127*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 67*x^75 + 4*x^74 + 85*x^73 + 78*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 58*x^68 + 103*x^67 + 92*x^66 + 97*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 25*x^27 + 92*x^26 + 79*x^25 + 58*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 78*x^20 + 125*x^19 + 4*x^18 + 59*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 103*x^11 + 116*x^10 + 81*x^9 + 54*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 114*x^4 + 91*x^3 + 108*x^2 + 77*x + 22, x^95 + 15*x^93 + 74*x^92 + 37*x^91 + 84*x^90 + 35*x^89 + 46*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 42*x^84 + 89*x^83 + 76*x^82 + 127*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 67*x^75 + 60*x^74 + 85*x^73 + 18*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 102*x^68 + 103*x^67 + 100*x^66 + 97*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 25*x^27 + 100*x^26 + 79*x^25 + 102*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 18*x^20 + 125*x^19 + 60*x^18 + 59*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 103*x^11 + 76*x^10 + 81*x^9 + 42*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 46*x^4 + 91*x^3 + 84*x^2 + 77*x + 74, x^95 + 15*x^93 + 22*x^92 + 5*x^91 + 108*x^90 + 67*x^89 + 114*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 54*x^84 + 121*x^83 + 116*x^82 + 95*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 99*x^75 + 4*x^74 + 53*x^73 + 78*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 58*x^68 + 71*x^67 + 92*x^66 + x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 121*x^27 + 92*x^26 + 111*x^25 + 58*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 78*x^20 + 29*x^19 + 4*x^18 + 27*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 7*x^11 + 116*x^10 + 49*x^9 + 54*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 114*x^4 + 59*x^3 + 108*x^2 + 109*x + 22, x^95 + 15*x^93 + 62*x^92 + 85*x^91 + 28*x^90 + 83*x^89 + 42*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 94*x^84 + 105*x^83 + 68*x^82 + 15*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 83*x^75 + 20*x^74 + 101*x^73 + 22*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 82*x^68 + 23*x^67 + 76*x^66 + 17*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 9*x^27 + 76*x^26 + 63*x^25 + 82*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 22*x^20 + 77*x^19 + 20*x^18 + 11*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 55*x^11 + 68*x^10 + 33*x^9 + 94*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 42*x^4 + 75*x^3 + 28*x^2 + 61*x + 62, x^95 + 15*x^93 + 18*x^92 + 101*x^91 + 20*x^90 + 3*x^89 + 54*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 18*x^84 + 25*x^83 + 76*x^82 + 31*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 3*x^75 + 124*x^74 + 117*x^73 + 74*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 126*x^68 + 39*x^67 + 100*x^66 + 65*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 89*x^27 + 36*x^26 + 47*x^25 + 14*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 26*x^20 + 61*x^19 + 60*x^18 + 91*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 39*x^11 + 12*x^10 + 113*x^9 + 2*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 102*x^4 + 27*x^3 + 84*x^2 + 45*x + 66, x^95 + 15*x^93 + 74*x^92 + 69*x^91 + 20*x^90 + 3*x^89 + 110*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 42*x^84 + 57*x^83 + 12*x^82 + 31*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 35*x^75 + 124*x^74 + 117*x^73 + 82*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 102*x^68 + 7*x^67 + 36*x^66 + 65*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 57*x^27 + 36*x^26 + 47*x^25 + 38*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 18*x^20 + 93*x^19 + 124*x^18 + 91*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 71*x^11 + 12*x^10 + 113*x^9 + 106*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 46*x^4 + 123*x^3 + 20*x^2 + 45*x + 10, x^95 + 15*x^93 + 118*x^92 + 101*x^91 + 108*x^90 + 99*x^89 + 82*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 22*x^84 + 25*x^83 + 116*x^82 + 63*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 3*x^75 + 4*x^74 + 21*x^73 + 110*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 90*x^68 + 39*x^67 + 92*x^66 + 33*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 89*x^27 + 92*x^26 + 15*x^25 + 26*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 46*x^20 + 61*x^19 + 4*x^18 + 123*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 39*x^11 + 116*x^10 + 17*x^9 + 86*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 18*x^4 + 27*x^3 + 108*x^2 + 13*x + 54, x^95 + 15*x^93 + 70*x^92 + 37*x^91 + 12*x^90 + 99*x^89 + 2*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 102*x^84 + 89*x^83 + 84*x^82 + 63*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 67*x^75 + 100*x^74 + 21*x^73 + 62*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 10*x^68 + 103*x^67 + 124*x^66 + 33*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 25*x^27 + 124*x^26 + 15*x^25 + 10*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 62*x^20 + 125*x^19 + 100*x^18 + 123*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 103*x^11 + 84*x^10 + 17*x^9 + 102*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 2*x^4 + 91*x^3 + 12*x^2 + 13*x + 70, x^95 + 15*x^93 + 2*x^92 + 69*x^91 + 84*x^90 + 99*x^89 + 102*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 66*x^84 + 57*x^83 + 12*x^82 + 63*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 35*x^75 + 60*x^74 + 21*x^73 + 26*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 78*x^68 + 7*x^67 + 36*x^66 + 33*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 57*x^27 + 100*x^26 + 15*x^25 + 126*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 10*x^20 + 93*x^19 + 124*x^18 + 123*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 71*x^11 + 76*x^10 + 17*x^9 + 18*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 118*x^4 + 123*x^3 + 20*x^2 + 13*x + 18, x^95 + 15*x^93 + 42*x^92 + 53*x^91 + 4*x^90 + 19*x^89 + 30*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 106*x^84 + 9*x^83 + 92*x^82 + 79*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 115*x^75 + 76*x^74 + 37*x^73 + 98*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 102*x^68 + 119*x^67 + 20*x^66 + 81*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 105*x^27 + 84*x^26 + 127*x^25 + 22*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 82*x^20 + 109*x^19 + 12*x^18 + 75*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 87*x^11 + 28*x^10 + 97*x^9 + 58*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 46*x^4 + 43*x^3 + 68*x^2 + 125*x + 58, x^95 + 15*x^93 + 106*x^92 + 37*x^91 + 116*x^90 + 35*x^89 + 46*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 10*x^84 + 89*x^83 + 44*x^82 + 127*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 67*x^75 + 28*x^74 + 85*x^73 + 18*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 6*x^68 + 103*x^67 + 4*x^66 + 97*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 25*x^27 + 4*x^26 + 79*x^25 + 102*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 114*x^20 + 125*x^19 + 28*x^18 + 59*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 103*x^11 + 44*x^10 + 81*x^9 + 42*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 78*x^4 + 91*x^3 + 116*x^2 + 77*x + 10, x^95 + 15*x^93 + 122*x^92 + 5*x^91 + 52*x^90 + 3*x^89 + 126*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 90*x^84 + 121*x^83 + 108*x^82 + 31*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 99*x^75 + 92*x^74 + 117*x^73 + 66*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 54*x^68 + 71*x^67 + 68*x^66 + 65*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 121*x^27 + 68*x^26 + 47*x^25 + 118*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 2*x^20 + 29*x^19 + 92*x^18 + 91*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 7*x^11 + 108*x^10 + 113*x^9 + 26*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 62*x^4 + 59*x^3 + 52*x^2 + 45*x + 58, x^95 + 15*x^93 + 30*x^92 + 53*x^91 + 28*x^90 + 51*x^89 + 74*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 62*x^84 + 9*x^83 + 68*x^82 + 47*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 115*x^75 + 20*x^74 + 5*x^73 + 118*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 114*x^68 + 119*x^67 + 76*x^66 + 113*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 105*x^27 + 76*x^26 + 31*x^25 + 114*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 118*x^20 + 109*x^19 + 20*x^18 + 43*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 87*x^11 + 68*x^10 + 65*x^9 + 62*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 74*x^4 + 43*x^3 + 28*x^2 + 29*x + 30, x^95 + 15*x^93 + 86*x^92 + 53*x^91 + 60*x^90 + 19*x^89 + 34*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 22*x^84 + 9*x^83 + 100*x^82 + 79*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 74*x^76 + 115*x^75 + 116*x^74 + 37*x^73 + 94*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 26*x^68 + 119*x^67 + 44*x^66 + 81*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 105*x^27 + 108*x^26 + 127*x^25 + 42*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 46*x^20 + 109*x^19 + 52*x^18 + 75*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 2*x^12 + 87*x^11 + 36*x^10 + 97*x^9 + 6*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 82*x^4 + 43*x^3 + 124*x^2 + 125*x + 6, x^95 + 15*x^93 + 38*x^92 + 53*x^91 + 92*x^90 + 19*x^89 + 18*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 102*x^84 + 9*x^83 + 68*x^82 + 79*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 115*x^75 + 84*x^74 + 37*x^73 + 110*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 74*x^68 + 119*x^67 + 76*x^66 + 81*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 105*x^27 + 12*x^26 + 127*x^25 + 90*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 62*x^20 + 109*x^19 + 20*x^18 + 75*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 87*x^11 + 4*x^10 + 97*x^9 + 86*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 66*x^4 + 43*x^3 + 28*x^2 + 125*x + 86, x^95 + 15*x^93 + 114*x^92 + 69*x^91 + 52*x^90 + 35*x^89 + 118*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 50*x^84 + 57*x^83 + 44*x^82 + 127*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 35*x^75 + 92*x^74 + 85*x^73 + 10*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 94*x^68 + 7*x^67 + 4*x^66 + 97*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 57*x^27 + 68*x^26 + 79*x^25 + 78*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 58*x^20 + 93*x^19 + 28*x^18 + 59*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 71*x^11 + 108*x^10 + 81*x^9 + 66*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 70*x^4 + 123*x^3 + 116*x^2 + 77*x + 66, x^95 + 15*x^93 + 122*x^92 + 85*x^91 + 68*x^90 + 51*x^89 + 46*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 122*x^84 + 105*x^83 + 28*x^82 + 47*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 83*x^75 + 12*x^74 + 5*x^73 + 82*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 86*x^68 + 23*x^67 + 84*x^66 + 113*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 9*x^27 + 20*x^26 + 31*x^25 + 102*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 34*x^20 + 77*x^19 + 76*x^18 + 43*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 55*x^11 + 92*x^10 + 65*x^9 + 106*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 94*x^4 + 75*x^3 + 4*x^2 + 29*x + 42, x^95 + 15*x^93 + 58*x^92 + 117*x^91 + 36*x^90 + 19*x^89 + 14*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 122*x^84 + 73*x^83 + 60*x^82 + 79*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 51*x^75 + 44*x^74 + 37*x^73 + 114*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 86*x^68 + 55*x^67 + 52*x^66 + 81*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 41*x^27 + 116*x^26 + 127*x^25 + 70*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 34*x^20 + 45*x^19 + 108*x^18 + 75*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 23*x^11 + 124*x^10 + 97*x^9 + 10*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 94*x^4 + 107*x^3 + 100*x^2 + 125*x + 10, x^95 + 15*x^93 + 50*x^92 + 53*x^91 + 68*x^90 + 51*x^89 + 102*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 18*x^84 + 9*x^83 + 92*x^82 + 47*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 115*x^75 + 12*x^74 + 5*x^73 + 90*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 62*x^68 + 119*x^67 + 20*x^66 + 113*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 105*x^27 + 20*x^26 + 31*x^25 + 126*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 26*x^20 + 109*x^19 + 12*x^18 + 43*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 87*x^11 + 92*x^10 + 65*x^9 + 82*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 38*x^4 + 43*x^3 + 68*x^2 + 29*x + 114, x^95 + 15*x^93 + 66*x^92 + 85*x^91 + 36*x^90 + 83*x^89 + 22*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 34*x^84 + 105*x^83 + 124*x^82 + 15*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 83*x^75 + 44*x^74 + 101*x^73 + 42*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 46*x^68 + 23*x^67 + 116*x^66 + 17*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 9*x^27 + 116*x^26 + 63*x^25 + 110*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 106*x^20 + 77*x^19 + 44*x^18 + 11*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 55*x^11 + 124*x^10 + 33*x^9 + 98*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 86*x^4 + 75*x^3 + 36*x^2 + 61*x + 2, x^95 + 15*x^93 + 22*x^92 + 101*x^91 + 12*x^90 + 99*x^89 + 82*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 118*x^84 + 25*x^83 + 84*x^82 + 63*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 3*x^75 + 100*x^74 + 21*x^73 + 110*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 122*x^68 + 39*x^67 + 124*x^66 + 33*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 89*x^27 + 124*x^26 + 15*x^25 + 26*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 14*x^20 + 61*x^19 + 100*x^18 + 123*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 39*x^11 + 84*x^10 + 17*x^9 + 86*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 50*x^4 + 27*x^3 + 12*x^2 + 13*x + 118, x^95 + 15*x^93 + 22*x^92 + 117*x^91 + 124*x^90 + 19*x^89 + 98*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 86*x^84 + 73*x^83 + 36*x^82 + 79*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 51*x^75 + 52*x^74 + 37*x^73 + 30*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 90*x^68 + 55*x^67 + 108*x^66 + 81*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 41*x^27 + 44*x^26 + 127*x^25 + 106*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 110*x^20 + 45*x^19 + 116*x^18 + 75*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 23*x^11 + 100*x^10 + 97*x^9 + 70*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 18*x^4 + 107*x^3 + 60*x^2 + 125*x + 70, x^95 + 15*x^93 + 14*x^92 + 117*x^91 + 124*x^90 + 51*x^89 + 90*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 46*x^84 + 73*x^83 + 100*x^82 + 47*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 51*x^75 + 52*x^74 + 5*x^73 + 102*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 2*x^68 + 55*x^67 + 44*x^66 + 113*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 41*x^27 + 44*x^26 + 31*x^25 + 66*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 38*x^20 + 45*x^19 + 52*x^18 + 43*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 23*x^11 + 100*x^10 + 65*x^9 + 110*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 26*x^4 + 107*x^3 + 124*x^2 + 29*x + 78, x^95 + 15*x^93 + 102*x^92 + 21*x^91 + 92*x^90 + 51*x^89 + 82*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 38*x^84 + 41*x^83 + 68*x^82 + 47*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 19*x^75 + 84*x^74 + 5*x^73 + 46*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 10*x^68 + 87*x^67 + 76*x^66 + 113*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 73*x^27 + 12*x^26 + 31*x^25 + 26*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 126*x^20 + 13*x^19 + 20*x^18 + 43*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 119*x^11 + 4*x^10 + 65*x^9 + 22*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 2*x^4 + 11*x^3 + 28*x^2 + 29*x + 22, x^95 + 15*x^93 + 30*x^92 + 101*x^91 + 44*x^90 + 67*x^89 + 58*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 94*x^84 + 25*x^83 + 116*x^82 + 95*x^81 + 106*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 3*x^75 + 68*x^74 + 53*x^73 + 70*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 18*x^68 + 39*x^67 + 92*x^66 + x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 89*x^27 + 28*x^26 + 111*x^25 + 34*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 22*x^20 + 61*x^19 + 4*x^18 + 27*x^17 + 82*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 39*x^11 + 52*x^10 + 49*x^9 + 78*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 106*x^4 + 27*x^3 + 108*x^2 + 109*x + 78, x^95 + 15*x^93 + 10*x^92 + 53*x^91 + 68*x^90 + 19*x^89 + 62*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 74*x^84 + 9*x^83 + 28*x^82 + 79*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 115*x^75 + 12*x^74 + 37*x^73 + 66*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 6*x^68 + 119*x^67 + 84*x^66 + 81*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 105*x^27 + 20*x^26 + 127*x^25 + 54*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 50*x^20 + 109*x^19 + 76*x^18 + 75*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 87*x^11 + 92*x^10 + 97*x^9 + 26*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 78*x^4 + 43*x^3 + 4*x^2 + 125*x + 26, x^95 + 15*x^93 + 114*x^92 + 21*x^91 + 36*x^90 + 83*x^89 + 70*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 18*x^84 + 41*x^83 + 124*x^82 + 15*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 19*x^75 + 44*x^74 + 101*x^73 + 122*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 62*x^68 + 87*x^67 + 116*x^66 + 17*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 73*x^27 + 116*x^26 + 63*x^25 + 94*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 26*x^20 + 13*x^19 + 44*x^18 + 11*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 119*x^11 + 124*x^10 + 33*x^9 + 114*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 38*x^4 + 11*x^3 + 36*x^2 + 61*x + 82, x^95 + 15*x^93 + 102*x^92 + 101*x^91 + 108*x^90 + 35*x^89 + 66*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 70*x^84 + 25*x^83 + 116*x^82 + 127*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 3*x^75 + 4*x^74 + 85*x^73 + 126*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 42*x^68 + 39*x^67 + 92*x^66 + 97*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 89*x^27 + 92*x^26 + 79*x^25 + 74*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 30*x^20 + 61*x^19 + 4*x^18 + 59*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 39*x^11 + 116*x^10 + 81*x^9 + 38*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 34*x^4 + 27*x^3 + 108*x^2 + 77*x + 70, x^95 + 15*x^93 + 10*x^92 + 101*x^91 + 116*x^90 + 99*x^89 + 78*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 42*x^84 + 25*x^83 + 44*x^82 + 63*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 3*x^75 + 28*x^74 + 21*x^73 + 114*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 102*x^68 + 39*x^67 + 4*x^66 + 33*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 89*x^27 + 4*x^26 + 15*x^25 + 6*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 18*x^20 + 61*x^19 + 28*x^18 + 123*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 39*x^11 + 44*x^10 + 17*x^9 + 10*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 46*x^4 + 27*x^3 + 116*x^2 + 13*x + 106, x^95 + 15*x^93 + 10*x^92 + 53*x^91 + 100*x^90 + 19*x^89 + 30*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 10*x^84 + 9*x^83 + 124*x^82 + 79*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 115*x^75 + 108*x^74 + 37*x^73 + 98*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 70*x^68 + 119*x^67 + 116*x^66 + 81*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 105*x^27 + 52*x^26 + 127*x^25 + 22*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 114*x^20 + 109*x^19 + 44*x^18 + 75*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 87*x^11 + 60*x^10 + 97*x^9 + 58*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 14*x^4 + 43*x^3 + 36*x^2 + 125*x + 122, x^95 + 15*x^93 + 106*x^92 + 101*x^91 + 52*x^90 + 35*x^89 + 46*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 10*x^84 + 25*x^83 + 108*x^82 + 127*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 3*x^75 + 92*x^74 + 85*x^73 + 18*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 6*x^68 + 39*x^67 + 68*x^66 + 97*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 89*x^27 + 68*x^26 + 79*x^25 + 102*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 114*x^20 + 61*x^19 + 92*x^18 + 59*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 39*x^11 + 108*x^10 + 81*x^9 + 42*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 78*x^4 + 27*x^3 + 52*x^2 + 77*x + 10, x^95 + 15*x^93 + 90*x^92 + 53*x^91 + 4*x^90 + 19*x^89 + 14*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 90*x^84 + 9*x^83 + 92*x^82 + 79*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 115*x^75 + 76*x^74 + 37*x^73 + 114*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 118*x^68 + 119*x^67 + 20*x^66 + 81*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 105*x^27 + 84*x^26 + 127*x^25 + 70*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 2*x^20 + 109*x^19 + 12*x^18 + 75*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 87*x^11 + 28*x^10 + 97*x^9 + 10*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 126*x^4 + 43*x^3 + 68*x^2 + 125*x + 74, x^95 + 15*x^93 + 34*x^92 + 53*x^91 + 4*x^90 + 51*x^89 + 86*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 66*x^84 + 9*x^83 + 28*x^82 + 47*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 115*x^75 + 76*x^74 + 5*x^73 + 106*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 14*x^68 + 119*x^67 + 84*x^66 + 113*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 105*x^27 + 84*x^26 + 31*x^25 + 46*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 10*x^20 + 109*x^19 + 76*x^18 + 43*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 87*x^11 + 28*x^10 + 65*x^9 + 34*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 54*x^4 + 43*x^3 + 4*x^2 + 29*x + 2, x^95 + 15*x^93 + 66*x^92 + 53*x^91 + 68*x^90 + 51*x^89 + 54*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 98*x^84 + 9*x^83 + 92*x^82 + 47*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 115*x^75 + 12*x^74 + 5*x^73 + 10*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 110*x^68 + 119*x^67 + 20*x^66 + 113*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 105*x^27 + 20*x^26 + 31*x^25 + 14*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 42*x^20 + 109*x^19 + 12*x^18 + 43*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 87*x^11 + 92*x^10 + 65*x^9 + 66*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 22*x^4 + 43*x^3 + 68*x^2 + 29*x + 34, x^95 + 15*x^93 + 38*x^92 + 37*x^91 + 12*x^90 + 99*x^89 + 98*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 70*x^84 + 89*x^83 + 84*x^82 + 63*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 67*x^75 + 100*x^74 + 21*x^73 + 94*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 42*x^68 + 103*x^67 + 124*x^66 + 33*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 25*x^27 + 124*x^26 + 15*x^25 + 106*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 30*x^20 + 125*x^19 + 100*x^18 + 123*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 103*x^11 + 84*x^10 + 17*x^9 + 6*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 34*x^4 + 91*x^3 + 12*x^2 + 13*x + 102, x^95 + 15*x^93 + 122*x^92 + 69*x^91 + 52*x^90 + 3*x^89 + 62*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 90*x^84 + 57*x^83 + 108*x^82 + 31*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 35*x^75 + 92*x^74 + 117*x^73 + 2*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 54*x^68 + 7*x^67 + 68*x^66 + 65*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 57*x^27 + 68*x^26 + 47*x^25 + 54*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 2*x^20 + 93*x^19 + 92*x^18 + 91*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 71*x^11 + 108*x^10 + 113*x^9 + 90*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 62*x^4 + 123*x^3 + 52*x^2 + 45*x + 122, x^95 + 15*x^93 + 14*x^92 + 69*x^91 + 108*x^90 + 99*x^89 + 42*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 14*x^84 + 57*x^83 + 52*x^82 + 63*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 35*x^75 + 4*x^74 + 21*x^73 + 86*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 98*x^68 + 7*x^67 + 28*x^66 + 33*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 57*x^27 + 92*x^26 + 15*x^25 + 82*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 6*x^20 + 93*x^19 + 68*x^18 + 123*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 71*x^11 + 116*x^10 + 17*x^9 + 30*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 122*x^4 + 123*x^3 + 44*x^2 + 13*x + 94, x^95 + 15*x^93 + 50*x^92 + 5*x^91 + 52*x^90 + 35*x^89 + 118*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 114*x^84 + 121*x^83 + 44*x^82 + 127*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 99*x^75 + 92*x^74 + 85*x^73 + 10*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 30*x^68 + 71*x^67 + 4*x^66 + 97*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 121*x^27 + 68*x^26 + 79*x^25 + 78*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 122*x^20 + 29*x^19 + 28*x^18 + 59*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 7*x^11 + 108*x^10 + 81*x^9 + 66*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 6*x^4 + 59*x^3 + 116*x^2 + 77*x + 66, x^95 + 15*x^93 + 122*x^92 + 85*x^91 + 68*x^90 + 115*x^89 + 110*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 122*x^84 + 105*x^83 + 28*x^82 + 111*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 83*x^75 + 12*x^74 + 69*x^73 + 18*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 86*x^68 + 23*x^67 + 84*x^66 + 49*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 9*x^27 + 20*x^26 + 95*x^25 + 38*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 34*x^20 + 77*x^19 + 76*x^18 + 107*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 55*x^11 + 92*x^10 + x^9 + 42*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 94*x^4 + 75*x^3 + 4*x^2 + 93*x + 106, x^95 + 15*x^93 + 54*x^92 + 117*x^91 + 60*x^90 + 19*x^89 + 66*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 118*x^84 + 73*x^83 + 100*x^82 + 79*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 51*x^75 + 116*x^74 + 37*x^73 + 62*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 58*x^68 + 55*x^67 + 44*x^66 + 81*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 41*x^27 + 108*x^26 + 127*x^25 + 74*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 14*x^20 + 45*x^19 + 52*x^18 + 75*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 23*x^11 + 36*x^10 + 97*x^9 + 102*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 114*x^4 + 107*x^3 + 124*x^2 + 125*x + 102, x^95 + 15*x^93 + 122*x^92 + 21*x^91 + 100*x^90 + 115*x^89 + 14*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 58*x^84 + 41*x^83 + 124*x^82 + 111*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 102*x^76 + 19*x^75 + 108*x^74 + 69*x^73 + 114*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 22*x^68 + 87*x^67 + 116*x^66 + 49*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 73*x^27 + 52*x^26 + 95*x^25 + 70*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 98*x^20 + 13*x^19 + 44*x^18 + 107*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 110*x^12 + 119*x^11 + 60*x^10 + x^9 + 10*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 30*x^4 + 11*x^3 + 36*x^2 + 93*x + 10, x^95 + 15*x^93 + 82*x^92 + 117*x^91 + 4*x^90 + 51*x^89 + 6*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 50*x^84 + 73*x^83 + 28*x^82 + 47*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 51*x^75 + 76*x^74 + 5*x^73 + 58*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 30*x^68 + 55*x^67 + 84*x^66 + 113*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 41*x^27 + 84*x^26 + 31*x^25 + 30*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 58*x^20 + 45*x^19 + 76*x^18 + 43*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 23*x^11 + 28*x^10 + 65*x^9 + 50*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 6*x^4 + 107*x^3 + 4*x^2 + 29*x + 82, x^95 + 15*x^93 + 10*x^92 + 117*x^91 + 36*x^90 + 19*x^89 + 30*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 10*x^84 + 73*x^83 + 60*x^82 + 79*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 51*x^75 + 44*x^74 + 37*x^73 + 98*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 70*x^68 + 55*x^67 + 52*x^66 + 81*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 41*x^27 + 116*x^26 + 127*x^25 + 22*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 114*x^20 + 45*x^19 + 108*x^18 + 75*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 23*x^11 + 124*x^10 + 97*x^9 + 58*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 14*x^4 + 107*x^3 + 100*x^2 + 125*x + 122, x^95 + 15*x^93 + 34*x^92 + 101*x^91 + 84*x^90 + 67*x^89 + 6*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 98*x^84 + 25*x^83 + 12*x^82 + 95*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 3*x^75 + 60*x^74 + 53*x^73 + 122*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 46*x^68 + 39*x^67 + 36*x^66 + x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 89*x^27 + 100*x^26 + 111*x^25 + 30*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 42*x^20 + 61*x^19 + 124*x^18 + 27*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 39*x^11 + 76*x^10 + 49*x^9 + 114*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 86*x^4 + 27*x^3 + 20*x^2 + 109*x + 114, x^95 + 15*x^93 + 54*x^92 + 5*x^91 + 12*x^90 + 3*x^89 + 50*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 22*x^84 + 121*x^83 + 84*x^82 + 31*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 99*x^75 + 100*x^74 + 117*x^73 + 14*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 90*x^68 + 71*x^67 + 124*x^66 + 65*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 121*x^27 + 124*x^26 + 47*x^25 + 122*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 46*x^20 + 29*x^19 + 100*x^18 + 91*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 7*x^11 + 84*x^10 + 113*x^9 + 118*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 18*x^4 + 59*x^3 + 12*x^2 + 45*x + 22, x^95 + 15*x^93 + 90*x^92 + 101*x^91 + 20*x^90 + 99*x^89 + 62*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 122*x^84 + 25*x^83 + 12*x^82 + 63*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 3*x^75 + 124*x^74 + 21*x^73 + 2*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 22*x^68 + 39*x^67 + 36*x^66 + 33*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 89*x^27 + 36*x^26 + 15*x^25 + 54*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 34*x^20 + 61*x^19 + 124*x^18 + 123*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 39*x^11 + 12*x^10 + 17*x^9 + 90*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 30*x^4 + 27*x^3 + 20*x^2 + 13*x + 58, x^95 + 15*x^93 + 50*x^92 + 37*x^91 + 84*x^90 + 67*x^89 + 22*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 50*x^84 + 89*x^83 + 12*x^82 + 95*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 67*x^75 + 60*x^74 + 53*x^73 + 106*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 94*x^68 + 103*x^67 + 36*x^66 + x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 25*x^27 + 100*x^26 + 111*x^25 + 110*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 58*x^20 + 125*x^19 + 124*x^18 + 27*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 103*x^11 + 76*x^10 + 49*x^9 + 34*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 70*x^4 + 91*x^3 + 20*x^2 + 109*x + 98, x^95 + 15*x^93 + 122*x^92 + 69*x^91 + 52*x^90 + 67*x^89 + 126*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 90*x^84 + 57*x^83 + 108*x^82 + 95*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 35*x^75 + 92*x^74 + 53*x^73 + 66*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 54*x^68 + 7*x^67 + 68*x^66 + x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 57*x^27 + 68*x^26 + 111*x^25 + 118*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 2*x^20 + 93*x^19 + 92*x^18 + 27*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 71*x^11 + 108*x^10 + 49*x^9 + 26*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 62*x^4 + 123*x^3 + 52*x^2 + 109*x + 58, x^95 + 15*x^93 + 98*x^92 + 5*x^91 + 52*x^90 + 35*x^89 + 102*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 98*x^84 + 121*x^83 + 44*x^82 + 127*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 99*x^75 + 92*x^74 + 85*x^73 + 26*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 46*x^68 + 71*x^67 + 4*x^66 + 97*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 121*x^27 + 68*x^26 + 79*x^25 + 126*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 42*x^20 + 29*x^19 + 28*x^18 + 59*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 7*x^11 + 108*x^10 + 81*x^9 + 18*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 86*x^4 + 59*x^3 + 116*x^2 + 77*x + 82, x^95 + 15*x^93 + 30*x^92 + 117*x^91 + 124*x^90 + 51*x^89 + 42*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 126*x^84 + 73*x^83 + 100*x^82 + 47*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 51*x^75 + 52*x^74 + 5*x^73 + 22*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 50*x^68 + 55*x^67 + 44*x^66 + 113*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 41*x^27 + 44*x^26 + 31*x^25 + 82*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 54*x^20 + 45*x^19 + 52*x^18 + 43*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 23*x^11 + 100*x^10 + 65*x^9 + 94*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 10*x^4 + 107*x^3 + 124*x^2 + 29*x + 126, x^95 + 15*x^93 + 42*x^92 + 85*x^91 + 100*x^90 + 51*x^89 + 126*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 42*x^84 + 105*x^83 + 124*x^82 + 47*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 54*x^76 + 83*x^75 + 108*x^74 + 5*x^73 + 2*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 38*x^68 + 23*x^67 + 116*x^66 + 113*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 9*x^27 + 52*x^26 + 31*x^25 + 118*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 18*x^20 + 77*x^19 + 44*x^18 + 43*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 126*x^12 + 55*x^11 + 60*x^10 + 65*x^9 + 90*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 110*x^4 + 75*x^3 + 36*x^2 + 29*x + 26, x^95 + 15*x^93 + 70*x^92 + 5*x^91 + 12*x^90 + 3*x^89 + 2*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 102*x^84 + 121*x^83 + 84*x^82 + 31*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 99*x^75 + 100*x^74 + 117*x^73 + 62*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 10*x^68 + 71*x^67 + 124*x^66 + 65*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 121*x^27 + 124*x^26 + 47*x^25 + 10*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 62*x^20 + 29*x^19 + 100*x^18 + 91*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 7*x^11 + 84*x^10 + 113*x^9 + 102*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 2*x^4 + 59*x^3 + 12*x^2 + 45*x + 70, x^95 + 15*x^93 + 58*x^92 + 101*x^91 + 116*x^90 + 99*x^89 + 62*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 26*x^84 + 25*x^83 + 44*x^82 + 63*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 3*x^75 + 28*x^74 + 21*x^73 + 2*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 118*x^68 + 39*x^67 + 4*x^66 + 33*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 89*x^27 + 4*x^26 + 15*x^25 + 54*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 66*x^20 + 61*x^19 + 28*x^18 + 123*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 39*x^11 + 44*x^10 + 17*x^9 + 90*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 126*x^4 + 27*x^3 + 116*x^2 + 13*x + 122, x^95 + 15*x^93 + 90*x^92 + 21*x^91 + 100*x^90 + 51*x^89 + 46*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 26*x^84 + 41*x^83 + 124*x^82 + 47*x^81 + 62*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 19*x^75 + 108*x^74 + 5*x^73 + 82*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 54*x^68 + 87*x^67 + 116*x^66 + 113*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 73*x^27 + 52*x^26 + 31*x^25 + 102*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 66*x^20 + 13*x^19 + 44*x^18 + 43*x^17 + 118*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 119*x^11 + 60*x^10 + 65*x^9 + 106*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 62*x^4 + 11*x^3 + 36*x^2 + 29*x + 106, x^95 + 15*x^93 + 6*x^92 + 101*x^91 + 44*x^90 + 99*x^89 + 98*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 102*x^84 + 25*x^83 + 52*x^82 + 63*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 3*x^75 + 68*x^74 + 21*x^73 + 94*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 10*x^68 + 39*x^67 + 28*x^66 + 33*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 89*x^27 + 28*x^26 + 15*x^25 + 106*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 62*x^20 + 61*x^19 + 68*x^18 + 123*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 39*x^11 + 52*x^10 + 17*x^9 + 6*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 2*x^4 + 27*x^3 + 44*x^2 + 13*x + 38, x^95 + 15*x^93 + 82*x^92 + 21*x^91 + 68*x^90 + 83*x^89 + 6*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 50*x^84 + 41*x^83 + 92*x^82 + 15*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 19*x^75 + 12*x^74 + 101*x^73 + 58*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 30*x^68 + 87*x^67 + 20*x^66 + 17*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 73*x^27 + 20*x^26 + 63*x^25 + 30*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 58*x^20 + 13*x^19 + 12*x^18 + 11*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 119*x^11 + 92*x^10 + 33*x^9 + 50*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 6*x^4 + 11*x^3 + 68*x^2 + 61*x + 82, x^95 + 15*x^93 + 118*x^92 + 69*x^91 + 12*x^90 + 67*x^89 + 114*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 86*x^84 + 57*x^83 + 84*x^82 + 95*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 35*x^75 + 100*x^74 + 53*x^73 + 78*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 26*x^68 + 7*x^67 + 124*x^66 + x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 57*x^27 + 124*x^26 + 111*x^25 + 58*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 110*x^20 + 93*x^19 + 100*x^18 + 27*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 71*x^11 + 84*x^10 + 49*x^9 + 54*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 82*x^4 + 123*x^3 + 12*x^2 + 109*x + 86, x^95 + 15*x^93 + 34*x^92 + 53*x^91 + 68*x^90 + 51*x^89 + 22*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 66*x^84 + 9*x^83 + 92*x^82 + 47*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 126*x^76 + 115*x^75 + 12*x^74 + 5*x^73 + 42*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 14*x^68 + 119*x^67 + 20*x^66 + 113*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 105*x^27 + 20*x^26 + 31*x^25 + 110*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 10*x^20 + 109*x^19 + 12*x^18 + 43*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 38*x^12 + 87*x^11 + 92*x^10 + 65*x^9 + 98*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 54*x^4 + 43*x^3 + 68*x^2 + 29*x + 66, x^95 + 15*x^93 + 18*x^92 + 117*x^91 + 100*x^90 + 115*x^89 + 38*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 50*x^84 + 73*x^83 + 60*x^82 + 111*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 51*x^75 + 108*x^74 + 69*x^73 + 26*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 30*x^68 + 55*x^67 + 52*x^66 + 49*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 41*x^27 + 52*x^26 + 95*x^25 + 62*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 58*x^20 + 45*x^19 + 108*x^18 + 107*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 23*x^11 + 60*x^10 + x^9 + 18*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 6*x^4 + 107*x^3 + 100*x^2 + 93*x + 114, x^95 + 15*x^93 + 98*x^92 + 85*x^91 + 36*x^90 + 19*x^89 + 118*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 66*x^84 + 105*x^83 + 124*x^82 + 79*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 83*x^75 + 44*x^74 + 37*x^73 + 74*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 14*x^68 + 23*x^67 + 116*x^66 + 81*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 9*x^27 + 116*x^26 + 127*x^25 + 78*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 10*x^20 + 77*x^19 + 44*x^18 + 75*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 55*x^11 + 124*x^10 + 97*x^9 + 2*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 54*x^4 + 75*x^3 + 36*x^2 + 125*x + 34, x^95 + 15*x^93 + 102*x^92 + 5*x^91 + 44*x^90 + 67*x^89 + 66*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 70*x^84 + 121*x^83 + 52*x^82 + 95*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 99*x^75 + 68*x^74 + 53*x^73 + 126*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 42*x^68 + 71*x^67 + 28*x^66 + x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 121*x^27 + 28*x^26 + 111*x^25 + 74*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 30*x^20 + 29*x^19 + 68*x^18 + 27*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 7*x^11 + 52*x^10 + 49*x^9 + 38*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 34*x^4 + 59*x^3 + 44*x^2 + 109*x + 70, x^95 + 15*x^93 + 70*x^92 + 21*x^91 + 92*x^90 + 115*x^89 + 114*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 6*x^84 + 41*x^83 + 68*x^82 + 111*x^81 + 98*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 19*x^75 + 84*x^74 + 69*x^73 + 14*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 42*x^68 + 87*x^67 + 76*x^66 + 49*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 73*x^27 + 12*x^26 + 95*x^25 + 58*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 94*x^20 + 13*x^19 + 20*x^18 + 107*x^17 + 42*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 119*x^11 + 4*x^10 + x^9 + 118*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 34*x^4 + 11*x^3 + 28*x^2 + 93*x + 118, x^95 + 15*x^93 + 22*x^92 + 101*x^91 + 76*x^90 + 35*x^89 + 82*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 118*x^84 + 25*x^83 + 20*x^82 + 127*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 3*x^75 + 36*x^74 + 85*x^73 + 110*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 122*x^68 + 39*x^67 + 60*x^66 + 97*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 89*x^27 + 60*x^26 + 79*x^25 + 26*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 14*x^20 + 61*x^19 + 36*x^18 + 59*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 39*x^11 + 20*x^10 + 81*x^9 + 86*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 50*x^4 + 27*x^3 + 76*x^2 + 77*x + 118, x^95 + 15*x^93 + 94*x^92 + 69*x^91 + 76*x^90 + 99*x^89 + 90*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 94*x^84 + 57*x^83 + 84*x^82 + 63*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 35*x^75 + 36*x^74 + 21*x^73 + 38*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 18*x^68 + 7*x^67 + 124*x^66 + 33*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 57*x^27 + 60*x^26 + 15*x^25 + 66*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 22*x^20 + 93*x^19 + 100*x^18 + 123*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 71*x^11 + 20*x^10 + 17*x^9 + 46*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 106*x^4 + 123*x^3 + 12*x^2 + 13*x + 110, x^95 + 15*x^93 + 106*x^92 + 53*x^91 + 36*x^90 + 83*x^89 + 126*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 106*x^84 + 9*x^83 + 60*x^82 + 15*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 115*x^75 + 44*x^74 + 101*x^73 + 2*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 102*x^68 + 119*x^67 + 52*x^66 + 17*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 105*x^27 + 116*x^26 + 63*x^25 + 118*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 82*x^20 + 109*x^19 + 108*x^18 + 11*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 87*x^11 + 124*x^10 + 33*x^9 + 90*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 46*x^4 + 43*x^3 + 100*x^2 + 61*x + 26, x^95 + 15*x^93 + 54*x^92 + 85*x^91 + 124*x^90 + 115*x^89 + 66*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 118*x^84 + 105*x^83 + 36*x^82 + 111*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 83*x^75 + 52*x^74 + 69*x^73 + 62*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 58*x^68 + 23*x^67 + 108*x^66 + 49*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 9*x^27 + 44*x^26 + 95*x^25 + 74*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 14*x^20 + 77*x^19 + 116*x^18 + 107*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 55*x^11 + 100*x^10 + x^9 + 102*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 114*x^4 + 75*x^3 + 60*x^2 + 93*x + 102, x^95 + 15*x^93 + 2*x^92 + 85*x^91 + 68*x^90 + 19*x^89 + 118*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 34*x^84 + 105*x^83 + 92*x^82 + 79*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 83*x^75 + 12*x^74 + 37*x^73 + 74*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 46*x^68 + 23*x^67 + 20*x^66 + 81*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 9*x^27 + 20*x^26 + 127*x^25 + 78*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 106*x^20 + 77*x^19 + 12*x^18 + 75*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 55*x^11 + 92*x^10 + 97*x^9 + 2*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 86*x^4 + 75*x^3 + 68*x^2 + 125*x + 98, x^95 + 15*x^93 + 18*x^92 + 117*x^91 + 4*x^90 + 51*x^89 + 70*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 114*x^84 + 73*x^83 + 28*x^82 + 47*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 51*x^75 + 76*x^74 + 5*x^73 + 122*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 94*x^68 + 55*x^67 + 84*x^66 + 113*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 41*x^27 + 84*x^26 + 31*x^25 + 94*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 122*x^20 + 45*x^19 + 76*x^18 + 43*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 23*x^11 + 28*x^10 + 65*x^9 + 114*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 70*x^4 + 107*x^3 + 4*x^2 + 29*x + 18, x^95 + 15*x^93 + 14*x^92 + 53*x^91 + 60*x^90 + 51*x^89 + 90*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 46*x^84 + 9*x^83 + 36*x^82 + 47*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 115*x^75 + 116*x^74 + 5*x^73 + 102*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 2*x^68 + 119*x^67 + 108*x^66 + 113*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 105*x^27 + 108*x^26 + 31*x^25 + 66*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 38*x^20 + 109*x^19 + 116*x^18 + 43*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 87*x^11 + 36*x^10 + 65*x^9 + 110*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 26*x^4 + 43*x^3 + 60*x^2 + 29*x + 78, x^95 + 15*x^93 + 54*x^92 + 37*x^91 + 44*x^90 + 99*x^89 + 18*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 86*x^84 + 89*x^83 + 52*x^82 + 63*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 67*x^75 + 68*x^74 + 21*x^73 + 46*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 26*x^68 + 103*x^67 + 28*x^66 + 33*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 25*x^27 + 28*x^26 + 15*x^25 + 90*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 110*x^20 + 125*x^19 + 68*x^18 + 123*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 103*x^11 + 52*x^10 + 17*x^9 + 22*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 82*x^4 + 91*x^3 + 44*x^2 + 13*x + 118, x^95 + 15*x^93 + 98*x^92 + 37*x^91 + 52*x^90 + 67*x^89 + 38*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 98*x^84 + 89*x^83 + 44*x^82 + 95*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 67*x^75 + 92*x^74 + 53*x^73 + 90*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 46*x^68 + 103*x^67 + 4*x^66 + x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 25*x^27 + 68*x^26 + 111*x^25 + 62*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 42*x^20 + 125*x^19 + 28*x^18 + 27*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 103*x^11 + 108*x^10 + 49*x^9 + 82*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 86*x^4 + 91*x^3 + 116*x^2 + 109*x + 18, x^95 + 15*x^93 + 74*x^92 + 117*x^91 + 4*x^90 + 19*x^89 + 126*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 10*x^84 + 73*x^83 + 92*x^82 + 79*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 51*x^75 + 76*x^74 + 37*x^73 + 2*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 70*x^68 + 55*x^67 + 20*x^66 + 81*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 41*x^27 + 84*x^26 + 127*x^25 + 118*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 114*x^20 + 45*x^19 + 12*x^18 + 75*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 23*x^11 + 28*x^10 + 97*x^9 + 90*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 14*x^4 + 107*x^3 + 68*x^2 + 125*x + 90, x^95 + 15*x^93 + 70*x^92 + 117*x^91 + 60*x^90 + 83*x^89 + 82*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 70*x^84 + 73*x^83 + 100*x^82 + 15*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 51*x^75 + 116*x^74 + 101*x^73 + 46*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 106*x^68 + 55*x^67 + 44*x^66 + 17*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 41*x^27 + 108*x^26 + 63*x^25 + 26*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 30*x^20 + 45*x^19 + 52*x^18 + 11*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 23*x^11 + 36*x^10 + 33*x^9 + 22*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 98*x^4 + 107*x^3 + 124*x^2 + 61*x + 86, x^95 + 15*x^93 + 94*x^92 + 117*x^91 + 92*x^90 + 51*x^89 + 10*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 126*x^84 + 73*x^83 + 4*x^82 + 47*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 51*x^75 + 84*x^74 + 5*x^73 + 54*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 50*x^68 + 55*x^67 + 12*x^66 + 113*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 41*x^27 + 12*x^26 + 31*x^25 + 50*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 54*x^20 + 45*x^19 + 84*x^18 + 43*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 23*x^11 + 4*x^10 + 65*x^9 + 126*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 10*x^4 + 107*x^3 + 92*x^2 + 29*x + 94, x^95 + 15*x^93 + 118*x^92 + 21*x^91 + 28*x^90 + 51*x^89 + 98*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 118*x^84 + 41*x^83 + 4*x^82 + 47*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 19*x^75 + 20*x^74 + 5*x^73 + 30*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 58*x^68 + 87*x^67 + 12*x^66 + 113*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 73*x^27 + 76*x^26 + 31*x^25 + 106*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 14*x^20 + 13*x^19 + 84*x^18 + 43*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 119*x^11 + 68*x^10 + 65*x^9 + 70*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 114*x^4 + 11*x^3 + 92*x^2 + 29*x + 6, x^95 + 15*x^93 + 14*x^92 + 37*x^91 + 44*x^90 + 3*x^89 + 106*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 14*x^84 + 89*x^83 + 116*x^82 + 31*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 67*x^75 + 68*x^74 + 117*x^73 + 22*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 98*x^68 + 103*x^67 + 92*x^66 + 65*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 25*x^27 + 28*x^26 + 47*x^25 + 18*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 6*x^20 + 125*x^19 + 4*x^18 + 91*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 103*x^11 + 52*x^10 + 113*x^9 + 94*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 122*x^4 + 91*x^3 + 108*x^2 + 45*x + 30, x^95 + 15*x^93 + 10*x^92 + 101*x^91 + 52*x^90 + 99*x^89 + 14*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 42*x^84 + 25*x^83 + 108*x^82 + 63*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 3*x^75 + 92*x^74 + 21*x^73 + 50*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 102*x^68 + 39*x^67 + 68*x^66 + 33*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 89*x^27 + 68*x^26 + 15*x^25 + 70*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 18*x^20 + 61*x^19 + 92*x^18 + 123*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 39*x^11 + 108*x^10 + 17*x^9 + 74*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 46*x^4 + 27*x^3 + 52*x^2 + 13*x + 42, x^95 + 15*x^93 + 98*x^92 + 85*x^91 + 36*x^90 + 83*x^89 + 54*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 66*x^84 + 105*x^83 + 124*x^82 + 15*x^81 + 102*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 83*x^75 + 44*x^74 + 101*x^73 + 10*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 14*x^68 + 23*x^67 + 116*x^66 + 17*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 9*x^27 + 116*x^26 + 63*x^25 + 14*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 10*x^20 + 77*x^19 + 44*x^18 + 11*x^17 + 62*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 55*x^11 + 124*x^10 + 33*x^9 + 66*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 54*x^4 + 75*x^3 + 36*x^2 + 61*x + 98, x^95 + 15*x^93 + 6*x^92 + 69*x^91 + 12*x^90 + 3*x^89 + 2*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 38*x^84 + 57*x^83 + 84*x^82 + 31*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 35*x^75 + 100*x^74 + 117*x^73 + 62*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 74*x^68 + 7*x^67 + 124*x^66 + 65*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 57*x^27 + 124*x^26 + 47*x^25 + 10*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 126*x^20 + 93*x^19 + 100*x^18 + 91*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 71*x^11 + 84*x^10 + 113*x^9 + 102*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 66*x^4 + 123*x^3 + 12*x^2 + 45*x + 70, x^95 + 15*x^93 + 50*x^92 + 85*x^91 + 68*x^90 + 83*x^89 + 38*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 18*x^84 + 105*x^83 + 92*x^82 + 15*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 83*x^75 + 12*x^74 + 101*x^73 + 26*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 62*x^68 + 23*x^67 + 20*x^66 + 17*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 9*x^27 + 20*x^26 + 63*x^25 + 62*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 26*x^20 + 77*x^19 + 12*x^18 + 11*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 55*x^11 + 92*x^10 + 33*x^9 + 18*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 38*x^4 + 75*x^3 + 68*x^2 + 61*x + 50, x^95 + 15*x^93 + 90*x^92 + 117*x^91 + 100*x^90 + 19*x^89 + 110*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 26*x^84 + 73*x^83 + 124*x^82 + 79*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 51*x^75 + 108*x^74 + 37*x^73 + 18*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 54*x^68 + 55*x^67 + 116*x^66 + 81*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 41*x^27 + 52*x^26 + 127*x^25 + 38*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 66*x^20 + 45*x^19 + 44*x^18 + 75*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 23*x^11 + 60*x^10 + 97*x^9 + 42*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 62*x^4 + 107*x^3 + 36*x^2 + 125*x + 42, x^95 + 15*x^93 + 110*x^92 + 5*x^91 + 44*x^90 + 35*x^89 + 74*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 110*x^84 + 121*x^83 + 116*x^82 + 127*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 99*x^75 + 68*x^74 + 85*x^73 + 54*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 2*x^68 + 71*x^67 + 92*x^66 + 97*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 121*x^27 + 28*x^26 + 79*x^25 + 114*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 102*x^20 + 29*x^19 + 4*x^18 + 59*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 7*x^11 + 52*x^10 + 81*x^9 + 126*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 26*x^4 + 59*x^3 + 108*x^2 + 77*x + 62, x^95 + 15*x^93 + 58*x^92 + 5*x^91 + 20*x^90 + 3*x^89 + 94*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 90*x^84 + 121*x^83 + 12*x^82 + 31*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 99*x^75 + 124*x^74 + 117*x^73 + 98*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 54*x^68 + 71*x^67 + 36*x^66 + 65*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 121*x^27 + 36*x^26 + 47*x^25 + 86*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 2*x^20 + 29*x^19 + 124*x^18 + 91*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 7*x^11 + 12*x^10 + 113*x^9 + 58*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 62*x^4 + 59*x^3 + 20*x^2 + 45*x + 26, x^95 + 15*x^93 + 18*x^92 + 69*x^91 + 52*x^90 + 35*x^89 + 22*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 82*x^84 + 57*x^83 + 44*x^82 + 127*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 35*x^75 + 92*x^74 + 85*x^73 + 106*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 62*x^68 + 7*x^67 + 4*x^66 + 97*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 57*x^27 + 68*x^26 + 79*x^25 + 110*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 90*x^20 + 93*x^19 + 28*x^18 + 59*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 71*x^11 + 108*x^10 + 81*x^9 + 34*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 38*x^4 + 123*x^3 + 116*x^2 + 77*x + 34, x^95 + 15*x^93 + 46*x^92 + 53*x^91 + 60*x^90 + 115*x^89 + 58*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 78*x^84 + 9*x^83 + 36*x^82 + 111*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 115*x^75 + 116*x^74 + 69*x^73 + 6*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 98*x^68 + 119*x^67 + 108*x^66 + 49*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 105*x^27 + 108*x^26 + 95*x^25 + 34*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 70*x^20 + 109*x^19 + 116*x^18 + 107*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 87*x^11 + 36*x^10 + x^9 + 14*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 122*x^4 + 43*x^3 + 60*x^2 + 93*x + 110, x^95 + 15*x^93 + 50*x^92 + 117*x^91 + 4*x^90 + 115*x^89 + 38*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 18*x^84 + 73*x^83 + 28*x^82 + 111*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 51*x^75 + 76*x^74 + 69*x^73 + 26*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 62*x^68 + 55*x^67 + 84*x^66 + 49*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 41*x^27 + 84*x^26 + 95*x^25 + 62*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 26*x^20 + 45*x^19 + 76*x^18 + 107*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 23*x^11 + 28*x^10 + x^9 + 18*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 38*x^4 + 107*x^3 + 4*x^2 + 93*x + 50, x^95 + 15*x^93 + 58*x^92 + 5*x^91 + 84*x^90 + 3*x^89 + 30*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 90*x^84 + 121*x^83 + 76*x^82 + 31*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 99*x^75 + 60*x^74 + 117*x^73 + 34*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 54*x^68 + 71*x^67 + 100*x^66 + 65*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 121*x^27 + 100*x^26 + 47*x^25 + 22*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 2*x^20 + 29*x^19 + 60*x^18 + 91*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 7*x^11 + 76*x^10 + 113*x^9 + 122*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 62*x^4 + 59*x^3 + 84*x^2 + 45*x + 90, x^95 + 15*x^93 + 2*x^92 + 5*x^91 + 84*x^90 + 35*x^89 + 102*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 66*x^84 + 121*x^83 + 12*x^82 + 127*x^81 + 54*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 99*x^75 + 60*x^74 + 85*x^73 + 26*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 78*x^68 + 71*x^67 + 36*x^66 + 97*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 121*x^27 + 100*x^26 + 79*x^25 + 126*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 10*x^20 + 29*x^19 + 124*x^18 + 59*x^17 + 78*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 7*x^11 + 76*x^10 + 81*x^9 + 18*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 118*x^4 + 59*x^3 + 20*x^2 + 77*x + 18, x^95 + 15*x^93 + 54*x^92 + 69*x^91 + 12*x^90 + 67*x^89 + 50*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 22*x^84 + 57*x^83 + 84*x^82 + 95*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 35*x^75 + 100*x^74 + 53*x^73 + 14*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 90*x^68 + 7*x^67 + 124*x^66 + x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 57*x^27 + 124*x^26 + 111*x^25 + 122*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 46*x^20 + 93*x^19 + 100*x^18 + 27*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 71*x^11 + 84*x^10 + 49*x^9 + 118*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 18*x^4 + 123*x^3 + 12*x^2 + 109*x + 22, x^95 + 15*x^93 + 18*x^92 + 37*x^91 + 52*x^90 + 3*x^89 + 86*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 82*x^84 + 89*x^83 + 44*x^82 + 31*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 67*x^75 + 92*x^74 + 117*x^73 + 42*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 62*x^68 + 103*x^67 + 4*x^66 + 65*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 25*x^27 + 68*x^26 + 47*x^25 + 46*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 90*x^20 + 125*x^19 + 28*x^18 + 91*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 103*x^11 + 108*x^10 + 113*x^9 + 98*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 38*x^4 + 91*x^3 + 116*x^2 + 45*x + 98, x^95 + 15*x^93 + 70*x^92 + 117*x^91 + 124*x^90 + 83*x^89 + 18*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 70*x^84 + 73*x^83 + 36*x^82 + 15*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 51*x^75 + 52*x^74 + 101*x^73 + 110*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 106*x^68 + 55*x^67 + 108*x^66 + 17*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 41*x^27 + 44*x^26 + 63*x^25 + 90*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 30*x^20 + 45*x^19 + 116*x^18 + 11*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 23*x^11 + 100*x^10 + 33*x^9 + 86*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 98*x^4 + 107*x^3 + 60*x^2 + 61*x + 22, x^95 + 15*x^93 + 106*x^92 + 117*x^91 + 68*x^90 + 83*x^89 + 30*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 42*x^84 + 73*x^83 + 28*x^82 + 15*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 51*x^75 + 12*x^74 + 101*x^73 + 98*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 38*x^68 + 55*x^67 + 84*x^66 + 17*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 41*x^27 + 20*x^26 + 63*x^25 + 22*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 18*x^20 + 45*x^19 + 76*x^18 + 11*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 23*x^11 + 92*x^10 + 33*x^9 + 58*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 110*x^4 + 107*x^3 + 4*x^2 + 61*x + 58, x^95 + 15*x^93 + 78*x^92 + 37*x^91 + 76*x^90 + 67*x^89 + 74*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 14*x^84 + 89*x^83 + 84*x^82 + 95*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 67*x^75 + 36*x^74 + 53*x^73 + 54*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 98*x^68 + 103*x^67 + 124*x^66 + x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 25*x^27 + 60*x^26 + 111*x^25 + 114*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 6*x^20 + 125*x^19 + 100*x^18 + 27*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 103*x^11 + 20*x^10 + 49*x^9 + 126*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 122*x^4 + 91*x^3 + 12*x^2 + 109*x + 126, x^95 + 15*x^93 + 86*x^92 + 5*x^91 + 12*x^90 + 67*x^89 + 18*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 54*x^84 + 121*x^83 + 84*x^82 + 95*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 99*x^75 + 100*x^74 + 53*x^73 + 46*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 58*x^68 + 71*x^67 + 124*x^66 + x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 121*x^27 + 124*x^26 + 111*x^25 + 90*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 78*x^20 + 29*x^19 + 100*x^18 + 27*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 7*x^11 + 84*x^10 + 49*x^9 + 22*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 114*x^4 + 59*x^3 + 12*x^2 + 109*x + 54, x^95 + 15*x^93 + 30*x^92 + 53*x^91 + 28*x^90 + 115*x^89 + 10*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 62*x^84 + 9*x^83 + 68*x^82 + 111*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 115*x^75 + 20*x^74 + 69*x^73 + 54*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 114*x^68 + 119*x^67 + 76*x^66 + 49*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 105*x^27 + 76*x^26 + 95*x^25 + 50*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 118*x^20 + 109*x^19 + 20*x^18 + 107*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 87*x^11 + 68*x^10 + x^9 + 126*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 74*x^4 + 43*x^3 + 28*x^2 + 93*x + 94, x^95 + 15*x^93 + 126*x^92 + 117*x^91 + 92*x^90 + 51*x^89 + 42*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 30*x^84 + 73*x^83 + 4*x^82 + 47*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 51*x^75 + 84*x^74 + 5*x^73 + 22*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 18*x^68 + 55*x^67 + 12*x^66 + 113*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 41*x^27 + 12*x^26 + 31*x^25 + 82*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 86*x^20 + 45*x^19 + 84*x^18 + 43*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 23*x^11 + 4*x^10 + 65*x^9 + 94*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 106*x^4 + 107*x^3 + 92*x^2 + 29*x + 62, x^95 + 15*x^93 + 98*x^92 + 5*x^91 + 84*x^90 + 35*x^89 + 70*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 34*x^84 + 121*x^83 + 12*x^82 + 127*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 99*x^75 + 60*x^74 + 85*x^73 + 58*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 110*x^68 + 71*x^67 + 36*x^66 + 97*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 121*x^27 + 100*x^26 + 79*x^25 + 94*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 106*x^20 + 29*x^19 + 124*x^18 + 59*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 7*x^11 + 76*x^10 + 81*x^9 + 50*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 22*x^4 + 59*x^3 + 20*x^2 + 77*x + 50, x^95 + 15*x^93 + 98*x^92 + 85*x^91 + 4*x^90 + 83*x^89 + 86*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 2*x^84 + 105*x^83 + 28*x^82 + 15*x^81 + 70*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 83*x^75 + 76*x^74 + 101*x^73 + 106*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 78*x^68 + 23*x^67 + 84*x^66 + 17*x^65 + 10*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 9*x^27 + 84*x^26 + 63*x^25 + 46*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 74*x^20 + 77*x^19 + 76*x^18 + 11*x^17 + 30*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 55*x^11 + 28*x^10 + 33*x^9 + 34*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 118*x^4 + 75*x^3 + 4*x^2 + 61*x + 2, x^95 + 15*x^93 + 114*x^92 + 21*x^91 + 36*x^90 + 19*x^89 + 6*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 18*x^84 + 41*x^83 + 124*x^82 + 79*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 46*x^76 + 19*x^75 + 44*x^74 + 37*x^73 + 58*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 62*x^68 + 87*x^67 + 116*x^66 + 81*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 73*x^27 + 116*x^26 + 127*x^25 + 30*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 26*x^20 + 13*x^19 + 44*x^18 + 75*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 22*x^12 + 119*x^11 + 124*x^10 + 97*x^9 + 50*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 38*x^4 + 11*x^3 + 36*x^2 + 125*x + 18, x^95 + 15*x^93 + 42*x^92 + 37*x^91 + 116*x^90 + 99*x^89 + 46*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 74*x^84 + 89*x^83 + 44*x^82 + 63*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 67*x^75 + 28*x^74 + 21*x^73 + 18*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 70*x^68 + 103*x^67 + 4*x^66 + 33*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 25*x^27 + 4*x^26 + 15*x^25 + 102*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 50*x^20 + 125*x^19 + 28*x^18 + 123*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 103*x^11 + 44*x^10 + 17*x^9 + 42*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 14*x^4 + 91*x^3 + 116*x^2 + 13*x + 10, x^95 + 15*x^93 + 18*x^92 + 21*x^91 + 36*x^90 + 83*x^89 + 102*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 50*x^84 + 41*x^83 + 124*x^82 + 15*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 19*x^75 + 44*x^74 + 101*x^73 + 90*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 30*x^68 + 87*x^67 + 116*x^66 + 17*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 73*x^27 + 116*x^26 + 63*x^25 + 126*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 58*x^20 + 13*x^19 + 44*x^18 + 11*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 119*x^11 + 124*x^10 + 33*x^9 + 82*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 6*x^4 + 11*x^3 + 36*x^2 + 61*x + 50, x^95 + 15*x^93 + 10*x^92 + 69*x^91 + 116*x^90 + 3*x^89 + 78*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 42*x^84 + 57*x^83 + 44*x^82 + 31*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 35*x^75 + 28*x^74 + 117*x^73 + 114*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 102*x^68 + 7*x^67 + 4*x^66 + 65*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 57*x^27 + 4*x^26 + 47*x^25 + 6*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 18*x^20 + 93*x^19 + 28*x^18 + 91*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 71*x^11 + 44*x^10 + 113*x^9 + 10*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 46*x^4 + 123*x^3 + 116*x^2 + 45*x + 106, x^95 + 15*x^93 + 110*x^92 + 21*x^91 + 92*x^90 + 83*x^89 + 26*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 78*x^84 + 41*x^83 + 4*x^82 + 15*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 19*x^75 + 84*x^74 + 101*x^73 + 38*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 98*x^68 + 87*x^67 + 12*x^66 + 17*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 73*x^27 + 12*x^26 + 63*x^25 + 2*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 70*x^20 + 13*x^19 + 84*x^18 + 11*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 119*x^11 + 4*x^10 + 33*x^9 + 46*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 122*x^4 + 11*x^3 + 92*x^2 + 61*x + 78, x^95 + 15*x^93 + 50*x^92 + 21*x^91 + 68*x^90 + 19*x^89 + 38*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 18*x^84 + 41*x^83 + 92*x^82 + 79*x^81 + 86*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 19*x^75 + 12*x^74 + 37*x^73 + 26*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 62*x^68 + 87*x^67 + 20*x^66 + 81*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 73*x^27 + 20*x^26 + 127*x^25 + 62*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 26*x^20 + 13*x^19 + 12*x^18 + 75*x^17 + 110*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 119*x^11 + 92*x^10 + 97*x^9 + 18*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 38*x^4 + 11*x^3 + 68*x^2 + 125*x + 50, x^95 + 15*x^93 + 18*x^92 + 101*x^91 + 52*x^90 + 67*x^89 + 86*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 82*x^84 + 25*x^83 + 44*x^82 + 95*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 3*x^75 + 92*x^74 + 53*x^73 + 42*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 62*x^68 + 39*x^67 + 4*x^66 + x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 89*x^27 + 68*x^26 + 111*x^25 + 46*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 90*x^20 + 61*x^19 + 28*x^18 + 27*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 39*x^11 + 108*x^10 + 49*x^9 + 98*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 38*x^4 + 27*x^3 + 116*x^2 + 109*x + 98, x^95 + 15*x^93 + 62*x^92 + 5*x^91 + 76*x^90 + 35*x^89 + 58*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 62*x^84 + 121*x^83 + 84*x^82 + 127*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 99*x^75 + 36*x^74 + 85*x^73 + 70*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 50*x^68 + 71*x^67 + 124*x^66 + 97*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 121*x^27 + 60*x^26 + 79*x^25 + 34*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 118*x^20 + 29*x^19 + 100*x^18 + 59*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 7*x^11 + 20*x^10 + 81*x^9 + 78*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 10*x^4 + 59*x^3 + 12*x^2 + 77*x + 14, x^95 + 15*x^93 + 110*x^92 + 69*x^91 + 12*x^90 + 99*x^89 + 106*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 46*x^84 + 57*x^83 + 20*x^82 + 63*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 35*x^75 + 100*x^74 + 21*x^73 + 22*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 66*x^68 + 7*x^67 + 60*x^66 + 33*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 57*x^27 + 124*x^26 + 15*x^25 + 18*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 38*x^20 + 93*x^19 + 36*x^18 + 123*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 71*x^11 + 84*x^10 + 17*x^9 + 94*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 90*x^4 + 123*x^3 + 76*x^2 + 13*x + 94, x^95 + 15*x^93 + 106*x^92 + 21*x^91 + 100*x^90 + 51*x^89 + 126*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 106*x^84 + 41*x^83 + 124*x^82 + 47*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 19*x^75 + 108*x^74 + 5*x^73 + 2*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 102*x^68 + 87*x^67 + 116*x^66 + 113*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 73*x^27 + 52*x^26 + 31*x^25 + 118*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 82*x^20 + 13*x^19 + 44*x^18 + 43*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 119*x^11 + 60*x^10 + 65*x^9 + 90*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 46*x^4 + 11*x^3 + 36*x^2 + 29*x + 26, x^95 + 15*x^93 + 38*x^92 + 85*x^91 + 92*x^90 + 51*x^89 + 82*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 102*x^84 + 105*x^83 + 68*x^82 + 47*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 83*x^75 + 84*x^74 + 5*x^73 + 46*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 74*x^68 + 23*x^67 + 76*x^66 + 113*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 9*x^27 + 12*x^26 + 31*x^25 + 26*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 62*x^20 + 77*x^19 + 20*x^18 + 43*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 55*x^11 + 4*x^10 + 65*x^9 + 22*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 66*x^4 + 75*x^3 + 28*x^2 + 29*x + 22, x^95 + 15*x^93 + 74*x^92 + 117*x^91 + 68*x^90 + 19*x^89 + 62*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 10*x^84 + 73*x^83 + 28*x^82 + 79*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 51*x^75 + 12*x^74 + 37*x^73 + 66*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 70*x^68 + 55*x^67 + 84*x^66 + 81*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 41*x^27 + 20*x^26 + 127*x^25 + 54*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 114*x^20 + 45*x^19 + 76*x^18 + 75*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 23*x^11 + 92*x^10 + 97*x^9 + 26*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 14*x^4 + 107*x^3 + 4*x^2 + 125*x + 26, x^95 + 15*x^93 + 102*x^92 + 5*x^91 + 44*x^90 + 3*x^89 + 2*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 70*x^84 + 121*x^83 + 52*x^82 + 31*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 99*x^75 + 68*x^74 + 117*x^73 + 62*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 42*x^68 + 71*x^67 + 28*x^66 + 65*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 121*x^27 + 28*x^26 + 47*x^25 + 10*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 30*x^20 + 29*x^19 + 68*x^18 + 91*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 7*x^11 + 52*x^10 + 113*x^9 + 102*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 34*x^4 + 59*x^3 + 44*x^2 + 45*x + 6, x^95 + 15*x^93 + 66*x^92 + 37*x^91 + 52*x^90 + 67*x^89 + 6*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 66*x^84 + 89*x^83 + 44*x^82 + 95*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 67*x^75 + 92*x^74 + 53*x^73 + 122*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 78*x^68 + 103*x^67 + 4*x^66 + x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 25*x^27 + 68*x^26 + 111*x^25 + 30*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 10*x^20 + 125*x^19 + 28*x^18 + 27*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 103*x^11 + 108*x^10 + 49*x^9 + 114*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 118*x^4 + 91*x^3 + 116*x^2 + 109*x + 50, x^95 + 15*x^93 + 26*x^92 + 101*x^91 + 20*x^90 + 35*x^89 + 62*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 58*x^84 + 25*x^83 + 12*x^82 + 127*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 6*x^76 + 3*x^75 + 124*x^74 + 85*x^73 + 2*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 86*x^68 + 39*x^67 + 36*x^66 + 97*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 2*x^28 + 89*x^27 + 36*x^26 + 79*x^25 + 54*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 98*x^20 + 61*x^19 + 124*x^18 + 59*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 14*x^12 + 39*x^11 + 12*x^10 + 81*x^9 + 90*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 94*x^4 + 27*x^3 + 20*x^2 + 77*x + 58, x^95 + 15*x^93 + 30*x^92 + 117*x^91 + 28*x^90 + 115*x^89 + 74*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 62*x^84 + 73*x^83 + 68*x^82 + 111*x^81 + 26*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 51*x^75 + 20*x^74 + 69*x^73 + 118*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 114*x^68 + 55*x^67 + 76*x^66 + 49*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 41*x^27 + 76*x^26 + 95*x^25 + 114*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 118*x^20 + 45*x^19 + 20*x^18 + 107*x^17 + 66*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 23*x^11 + 68*x^10 + x^9 + 62*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 74*x^4 + 107*x^3 + 28*x^2 + 93*x + 30, x^95 + 15*x^93 + 78*x^92 + 53*x^91 + 28*x^90 + 51*x^89 + 58*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 46*x^84 + 9*x^83 + 68*x^82 + 47*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 115*x^75 + 20*x^74 + 5*x^73 + 6*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 2*x^68 + 119*x^67 + 76*x^66 + 113*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 105*x^27 + 76*x^26 + 31*x^25 + 34*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 38*x^20 + 109*x^19 + 20*x^18 + 43*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 87*x^11 + 68*x^10 + 65*x^9 + 14*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 26*x^4 + 43*x^3 + 28*x^2 + 29*x + 46, x^95 + 15*x^93 + 34*x^92 + 5*x^91 + 116*x^90 + 35*x^89 + 102*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 34*x^84 + 121*x^83 + 108*x^82 + 127*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 62*x^76 + 99*x^75 + 28*x^74 + 85*x^73 + 26*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 110*x^68 + 71*x^67 + 68*x^66 + 97*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 42*x^28 + 121*x^27 + 4*x^26 + 79*x^25 + 126*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 106*x^20 + 29*x^19 + 92*x^18 + 59*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 102*x^12 + 7*x^11 + 44*x^10 + 81*x^9 + 18*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 22*x^4 + 59*x^3 + 52*x^2 + 77*x + 82, x^95 + 15*x^93 + 90*x^92 + 21*x^91 + 36*x^90 + 51*x^89 + 110*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 26*x^84 + 41*x^83 + 60*x^82 + 47*x^81 + 126*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 19*x^75 + 44*x^74 + 5*x^73 + 18*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 54*x^68 + 87*x^67 + 52*x^66 + 113*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 12*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 36*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 73*x^27 + 116*x^26 + 31*x^25 + 38*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 66*x^20 + 13*x^19 + 108*x^18 + 43*x^17 + 54*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 119*x^11 + 124*x^10 + 65*x^9 + 42*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 62*x^4 + 11*x^3 + 100*x^2 + 29*x + 42, x^95 + 15*x^93 + 82*x^92 + 5*x^91 + 84*x^90 + 99*x^89 + 54*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 82*x^84 + 121*x^83 + 12*x^82 + 63*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 99*x^75 + 60*x^74 + 21*x^73 + 74*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 62*x^68 + 71*x^67 + 36*x^66 + 33*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 121*x^27 + 100*x^26 + 15*x^25 + 14*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 90*x^20 + 29*x^19 + 124*x^18 + 123*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 7*x^11 + 76*x^10 + 17*x^9 + 2*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 38*x^4 + 59*x^3 + 20*x^2 + 13*x + 66, x^95 + 15*x^93 + 82*x^92 + 5*x^91 + 52*x^90 + 35*x^89 + 22*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 18*x^84 + 121*x^83 + 44*x^82 + 127*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 14*x^76 + 99*x^75 + 92*x^74 + 85*x^73 + 106*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 126*x^68 + 71*x^67 + 4*x^66 + 97*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 121*x^27 + 68*x^26 + 79*x^25 + 110*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 26*x^20 + 29*x^19 + 28*x^18 + 59*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 118*x^12 + 7*x^11 + 108*x^10 + 81*x^9 + 34*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 102*x^4 + 59*x^3 + 116*x^2 + 77*x + 34, x^95 + 15*x^93 + 14*x^92 + 53*x^91 + 124*x^90 + 51*x^89 + 26*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 46*x^84 + 9*x^83 + 100*x^82 + 47*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 115*x^75 + 52*x^74 + 5*x^73 + 38*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 2*x^68 + 119*x^67 + 44*x^66 + 113*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 105*x^27 + 44*x^26 + 31*x^25 + 2*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 38*x^20 + 109*x^19 + 52*x^18 + 43*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 87*x^11 + 100*x^10 + 65*x^9 + 46*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 26*x^4 + 43*x^3 + 124*x^2 + 29*x + 14, x^95 + 15*x^93 + 50*x^92 + 117*x^91 + 68*x^90 + 115*x^89 + 102*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 18*x^84 + 73*x^83 + 92*x^82 + 111*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 51*x^75 + 12*x^74 + 69*x^73 + 90*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 62*x^68 + 55*x^67 + 20*x^66 + 49*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 41*x^27 + 20*x^26 + 95*x^25 + 126*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 26*x^20 + 45*x^19 + 12*x^18 + 107*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 23*x^11 + 92*x^10 + x^9 + 82*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 38*x^4 + 107*x^3 + 68*x^2 + 93*x + 114, x^95 + 15*x^93 + 126*x^92 + 117*x^91 + 28*x^90 + 51*x^89 + 106*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 30*x^84 + 73*x^83 + 68*x^82 + 47*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 51*x^75 + 20*x^74 + 5*x^73 + 86*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 18*x^68 + 55*x^67 + 76*x^66 + 113*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 41*x^27 + 76*x^26 + 31*x^25 + 18*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 86*x^20 + 45*x^19 + 20*x^18 + 43*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 23*x^11 + 68*x^10 + 65*x^9 + 30*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 106*x^4 + 107*x^3 + 28*x^2 + 29*x + 126, x^95 + 15*x^93 + 42*x^92 + 5*x^91 + 20*x^90 + 3*x^89 + 14*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 10*x^84 + 121*x^83 + 12*x^82 + 31*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 99*x^75 + 124*x^74 + 117*x^73 + 50*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 6*x^68 + 71*x^67 + 36*x^66 + 65*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 121*x^27 + 36*x^26 + 47*x^25 + 70*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 114*x^20 + 29*x^19 + 124*x^18 + 91*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 7*x^11 + 12*x^10 + 113*x^9 + 74*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 78*x^4 + 59*x^3 + 20*x^2 + 45*x + 106, x^95 + 15*x^93 + 62*x^92 + 117*x^91 + 28*x^90 + 51*x^89 + 42*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 94*x^84 + 73*x^83 + 68*x^82 + 47*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 51*x^75 + 20*x^74 + 5*x^73 + 22*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 82*x^68 + 55*x^67 + 76*x^66 + 113*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 41*x^27 + 76*x^26 + 31*x^25 + 82*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 22*x^20 + 45*x^19 + 20*x^18 + 43*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 23*x^11 + 68*x^10 + 65*x^9 + 94*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 42*x^4 + 107*x^3 + 28*x^2 + 29*x + 62, x^95 + 15*x^93 + 42*x^92 + 69*x^91 + 116*x^90 + 3*x^89 + 110*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 74*x^84 + 57*x^83 + 44*x^82 + 31*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 35*x^75 + 28*x^74 + 117*x^73 + 82*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 70*x^68 + 7*x^67 + 4*x^66 + 65*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 57*x^27 + 4*x^26 + 47*x^25 + 38*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 50*x^20 + 93*x^19 + 28*x^18 + 91*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 71*x^11 + 44*x^10 + 113*x^9 + 106*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 14*x^4 + 123*x^3 + 116*x^2 + 45*x + 74, x^95 + 15*x^93 + 42*x^92 + 37*x^91 + 20*x^90 + 99*x^89 + 14*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 10*x^84 + 89*x^83 + 12*x^82 + 63*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 67*x^75 + 124*x^74 + 21*x^73 + 50*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 6*x^68 + 103*x^67 + 36*x^66 + 33*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 25*x^27 + 36*x^26 + 15*x^25 + 70*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 114*x^20 + 125*x^19 + 124*x^18 + 123*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 103*x^11 + 12*x^10 + 17*x^9 + 74*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 78*x^4 + 91*x^3 + 20*x^2 + 13*x + 106, x^95 + 15*x^93 + 122*x^92 + 37*x^91 + 116*x^90 + 35*x^89 + 126*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 90*x^84 + 89*x^83 + 44*x^82 + 127*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 67*x^75 + 28*x^74 + 85*x^73 + 66*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 54*x^68 + 103*x^67 + 4*x^66 + 97*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 25*x^27 + 4*x^26 + 79*x^25 + 118*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 2*x^20 + 125*x^19 + 28*x^18 + 59*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 103*x^11 + 44*x^10 + 81*x^9 + 26*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 62*x^4 + 91*x^3 + 116*x^2 + 77*x + 58, x^95 + 15*x^93 + 10*x^92 + 37*x^91 + 20*x^90 + 99*x^89 + 110*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 106*x^84 + 89*x^83 + 12*x^82 + 63*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 67*x^75 + 124*x^74 + 21*x^73 + 82*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 38*x^68 + 103*x^67 + 36*x^66 + 33*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 25*x^27 + 36*x^26 + 15*x^25 + 38*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 82*x^20 + 125*x^19 + 124*x^18 + 123*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 103*x^11 + 12*x^10 + 17*x^9 + 106*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 110*x^4 + 91*x^3 + 20*x^2 + 13*x + 10, x^95 + 15*x^93 + 54*x^92 + 53*x^91 + 28*x^90 + 83*x^89 + 98*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 54*x^84 + 9*x^83 + 4*x^82 + 15*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 115*x^75 + 20*x^74 + 101*x^73 + 30*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 122*x^68 + 119*x^67 + 12*x^66 + 17*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 105*x^27 + 76*x^26 + 63*x^25 + 106*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 78*x^20 + 109*x^19 + 84*x^18 + 11*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 87*x^11 + 68*x^10 + 33*x^9 + 70*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 50*x^4 + 43*x^3 + 92*x^2 + 61*x + 6, x^95 + 15*x^93 + 10*x^92 + 21*x^91 + 68*x^90 + 115*x^89 + 126*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 74*x^84 + 41*x^83 + 28*x^82 + 111*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 19*x^75 + 12*x^74 + 69*x^73 + 2*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 6*x^68 + 87*x^67 + 84*x^66 + 49*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 73*x^27 + 20*x^26 + 95*x^25 + 118*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 50*x^20 + 13*x^19 + 76*x^18 + 107*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 119*x^11 + 92*x^10 + x^9 + 90*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 78*x^4 + 11*x^3 + 4*x^2 + 93*x + 90, x^95 + 15*x^93 + 18*x^92 + 85*x^91 + 36*x^90 + 83*x^89 + 38*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 50*x^84 + 105*x^83 + 124*x^82 + 15*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 14*x^76 + 83*x^75 + 44*x^74 + 101*x^73 + 26*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 30*x^68 + 23*x^67 + 116*x^66 + 17*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 9*x^27 + 116*x^26 + 63*x^25 + 62*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 58*x^20 + 77*x^19 + 44*x^18 + 11*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 118*x^12 + 55*x^11 + 124*x^10 + 33*x^9 + 18*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 6*x^4 + 75*x^3 + 36*x^2 + 61*x + 114, x^95 + 15*x^93 + 46*x^92 + 101*x^91 + 108*x^90 + 67*x^89 + 74*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 46*x^84 + 25*x^83 + 52*x^82 + 95*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 114*x^76 + 3*x^75 + 4*x^74 + 53*x^73 + 54*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 66*x^68 + 39*x^67 + 28*x^66 + x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 89*x^27 + 92*x^26 + 111*x^25 + 114*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 38*x^20 + 61*x^19 + 68*x^18 + 27*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 10*x^12 + 39*x^11 + 116*x^10 + 49*x^9 + 126*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 90*x^4 + 27*x^3 + 44*x^2 + 109*x + 62, x^95 + 15*x^93 + 22*x^92 + 85*x^91 + 60*x^90 + 115*x^89 + 98*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 86*x^84 + 105*x^83 + 100*x^82 + 111*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 10*x^76 + 83*x^75 + 116*x^74 + 69*x^73 + 30*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 90*x^68 + 23*x^67 + 44*x^66 + 49*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 92*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 116*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 9*x^27 + 108*x^26 + 95*x^25 + 106*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 110*x^20 + 77*x^19 + 52*x^18 + 107*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 66*x^12 + 55*x^11 + 36*x^10 + x^9 + 70*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 18*x^4 + 75*x^3 + 124*x^2 + 93*x + 70, x^95 + 15*x^93 + 46*x^92 + 85*x^91 + 92*x^90 + 19*x^89 + 90*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 14*x^84 + 105*x^83 + 4*x^82 + 79*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 83*x^75 + 84*x^74 + 37*x^73 + 102*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 34*x^68 + 23*x^67 + 12*x^66 + 81*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 9*x^27 + 12*x^26 + 127*x^25 + 66*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 6*x^20 + 77*x^19 + 84*x^18 + 75*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 55*x^11 + 4*x^10 + 97*x^9 + 110*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 58*x^4 + 75*x^3 + 92*x^2 + 125*x + 14, x^95 + 15*x^93 + 58*x^92 + 53*x^91 + 36*x^90 + 83*x^89 + 14*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 122*x^84 + 9*x^83 + 60*x^82 + 15*x^81 + 30*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 38*x^76 + 115*x^75 + 44*x^74 + 101*x^73 + 114*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 86*x^68 + 119*x^67 + 52*x^66 + 17*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 68*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 108*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 105*x^27 + 116*x^26 + 63*x^25 + 70*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 34*x^20 + 109*x^19 + 108*x^18 + 11*x^17 + 86*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 46*x^12 + 87*x^11 + 124*x^10 + 33*x^9 + 10*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 94*x^4 + 43*x^3 + 100*x^2 + 61*x + 10, x^95 + 15*x^93 + 94*x^92 + 21*x^91 + 124*x^90 + 83*x^89 + 42*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 62*x^84 + 41*x^83 + 100*x^82 + 15*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 19*x^75 + 52*x^74 + 101*x^73 + 22*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 114*x^68 + 87*x^67 + 44*x^66 + 17*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 73*x^27 + 44*x^26 + 63*x^25 + 82*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 118*x^20 + 13*x^19 + 52*x^18 + 11*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 119*x^11 + 100*x^10 + 33*x^9 + 94*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 74*x^4 + 11*x^3 + 124*x^2 + 61*x + 126, x^95 + 15*x^93 + 126*x^92 + 21*x^91 + 92*x^90 + 83*x^89 + 106*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 30*x^84 + 41*x^83 + 4*x^82 + 15*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 19*x^75 + 84*x^74 + 101*x^73 + 86*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 18*x^68 + 87*x^67 + 12*x^66 + 17*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 73*x^27 + 12*x^26 + 63*x^25 + 18*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 86*x^20 + 13*x^19 + 84*x^18 + 11*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 119*x^11 + 4*x^10 + 33*x^9 + 30*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 106*x^4 + 11*x^3 + 92*x^2 + 61*x + 126, x^95 + 15*x^93 + 110*x^92 + 101*x^91 + 12*x^90 + 67*x^89 + 106*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 46*x^84 + 25*x^83 + 20*x^82 + 95*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 3*x^75 + 100*x^74 + 53*x^73 + 22*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 66*x^68 + 39*x^67 + 60*x^66 + x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 89*x^27 + 124*x^26 + 111*x^25 + 18*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 38*x^20 + 61*x^19 + 36*x^18 + 27*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 39*x^11 + 84*x^10 + 49*x^9 + 94*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 90*x^4 + 27*x^3 + 76*x^2 + 109*x + 94, x^95 + 15*x^93 + 62*x^92 + 21*x^91 + 92*x^90 + 83*x^89 + 42*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 94*x^84 + 41*x^83 + 4*x^82 + 15*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 19*x^75 + 84*x^74 + 101*x^73 + 22*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 82*x^68 + 87*x^67 + 12*x^66 + 17*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 73*x^27 + 12*x^26 + 63*x^25 + 82*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 22*x^20 + 13*x^19 + 84*x^18 + 11*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 119*x^11 + 4*x^10 + 33*x^9 + 94*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 42*x^4 + 11*x^3 + 92*x^2 + 61*x + 62, x^95 + 15*x^93 + 2*x^92 + 53*x^91 + 100*x^90 + 51*x^89 + 86*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 98*x^84 + 9*x^83 + 60*x^82 + 47*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 115*x^75 + 108*x^74 + 5*x^73 + 106*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 110*x^68 + 119*x^67 + 52*x^66 + 113*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 105*x^27 + 52*x^26 + 31*x^25 + 46*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 42*x^20 + 109*x^19 + 108*x^18 + 43*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 87*x^11 + 60*x^10 + 65*x^9 + 34*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 22*x^4 + 43*x^3 + 100*x^2 + 29*x + 66, x^95 + 15*x^93 + 122*x^92 + 37*x^91 + 84*x^90 + 35*x^89 + 30*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 26*x^84 + 89*x^83 + 76*x^82 + 127*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 67*x^75 + 60*x^74 + 85*x^73 + 34*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 118*x^68 + 103*x^67 + 100*x^66 + 97*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 25*x^27 + 100*x^26 + 79*x^25 + 22*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 66*x^20 + 125*x^19 + 60*x^18 + 59*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 103*x^11 + 76*x^10 + 81*x^9 + 122*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 126*x^4 + 91*x^3 + 84*x^2 + 77*x + 90, x^95 + 15*x^93 + 2*x^92 + 37*x^91 + 52*x^90 + 3*x^89 + 6*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 2*x^84 + 89*x^83 + 44*x^82 + 31*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 67*x^75 + 92*x^74 + 117*x^73 + 122*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 14*x^68 + 103*x^67 + 4*x^66 + 65*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 25*x^27 + 68*x^26 + 47*x^25 + 30*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 74*x^20 + 125*x^19 + 28*x^18 + 91*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 103*x^11 + 108*x^10 + 113*x^9 + 114*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 54*x^4 + 91*x^3 + 116*x^2 + 45*x + 50, x^95 + 15*x^93 + 50*x^92 + 37*x^91 + 20*x^90 + 3*x^89 + 22*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 50*x^84 + 89*x^83 + 76*x^82 + 31*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 67*x^75 + 124*x^74 + 117*x^73 + 106*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 94*x^68 + 103*x^67 + 100*x^66 + 65*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 25*x^27 + 36*x^26 + 47*x^25 + 110*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 58*x^20 + 125*x^19 + 60*x^18 + 91*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 103*x^11 + 12*x^10 + 113*x^9 + 34*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 70*x^4 + 91*x^3 + 84*x^2 + 45*x + 98, x^95 + 15*x^93 + 70*x^92 + 53*x^91 + 92*x^90 + 19*x^89 + 50*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 6*x^84 + 9*x^83 + 68*x^82 + 79*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 115*x^75 + 84*x^74 + 37*x^73 + 78*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 42*x^68 + 119*x^67 + 76*x^66 + 81*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 105*x^27 + 12*x^26 + 127*x^25 + 122*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 94*x^20 + 109*x^19 + 20*x^18 + 75*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 87*x^11 + 4*x^10 + 97*x^9 + 54*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 34*x^4 + 43*x^3 + 28*x^2 + 125*x + 54, x^95 + 15*x^93 + 50*x^92 + 37*x^91 + 20*x^90 + 67*x^89 + 86*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 50*x^84 + 89*x^83 + 76*x^82 + 95*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 67*x^75 + 124*x^74 + 53*x^73 + 42*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 94*x^68 + 103*x^67 + 100*x^66 + x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 25*x^27 + 36*x^26 + 111*x^25 + 46*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 58*x^20 + 125*x^19 + 60*x^18 + 27*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 103*x^11 + 12*x^10 + 49*x^9 + 98*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 70*x^4 + 91*x^3 + 84*x^2 + 109*x + 34, x^95 + 15*x^93 + 70*x^92 + 21*x^91 + 28*x^90 + 115*x^89 + 50*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 6*x^84 + 41*x^83 + 4*x^82 + 111*x^81 + 34*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 19*x^75 + 20*x^74 + 69*x^73 + 78*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 42*x^68 + 87*x^67 + 12*x^66 + 49*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 52*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 28*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 73*x^27 + 76*x^26 + 95*x^25 + 122*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 94*x^20 + 13*x^19 + 84*x^18 + 107*x^17 + 106*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 119*x^11 + 68*x^10 + x^9 + 54*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 34*x^4 + 11*x^3 + 92*x^2 + 93*x + 54, x^95 + 15*x^93 + 90*x^92 + 21*x^91 + 4*x^90 + 51*x^89 + 14*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 90*x^84 + 41*x^83 + 92*x^82 + 47*x^81 + 94*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 6*x^76 + 19*x^75 + 76*x^74 + 5*x^73 + 114*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 118*x^68 + 87*x^67 + 20*x^66 + 113*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 76*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 4*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 100*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 44*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 73*x^27 + 84*x^26 + 31*x^25 + 70*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 2*x^20 + 13*x^19 + 12*x^18 + 43*x^17 + 22*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 14*x^12 + 119*x^11 + 28*x^10 + 65*x^9 + 10*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 126*x^4 + 11*x^3 + 68*x^2 + 29*x + 74, x^95 + 15*x^93 + 42*x^92 + 5*x^91 + 116*x^90 + 3*x^89 + 46*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 74*x^84 + 121*x^83 + 44*x^82 + 31*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 99*x^75 + 28*x^74 + 117*x^73 + 18*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 70*x^68 + 71*x^67 + 4*x^66 + 65*x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 121*x^27 + 4*x^26 + 47*x^25 + 102*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 50*x^20 + 29*x^19 + 28*x^18 + 91*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 7*x^11 + 44*x^10 + 113*x^9 + 42*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 14*x^4 + 59*x^3 + 116*x^2 + 45*x + 10, x^95 + 15*x^93 + 106*x^92 + 37*x^91 + 20*x^90 + 99*x^89 + 78*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 74*x^84 + 89*x^83 + 12*x^82 + 63*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 67*x^75 + 124*x^74 + 21*x^73 + 114*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 70*x^68 + 103*x^67 + 36*x^66 + 33*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 25*x^27 + 36*x^26 + 15*x^25 + 6*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 50*x^20 + 125*x^19 + 124*x^18 + 123*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 103*x^11 + 12*x^10 + 17*x^9 + 10*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 14*x^4 + 91*x^3 + 20*x^2 + 13*x + 42, x^95 + 15*x^93 + 10*x^92 + 69*x^91 + 52*x^90 + 3*x^89 + 14*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 42*x^84 + 57*x^83 + 108*x^82 + 31*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 35*x^75 + 92*x^74 + 117*x^73 + 50*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 102*x^68 + 7*x^67 + 68*x^66 + 65*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 57*x^27 + 68*x^26 + 47*x^25 + 70*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 18*x^20 + 93*x^19 + 92*x^18 + 91*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 71*x^11 + 108*x^10 + 113*x^9 + 74*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 46*x^4 + 123*x^3 + 52*x^2 + 45*x + 42, x^95 + 15*x^93 + 14*x^92 + 53*x^91 + 28*x^90 + 115*x^89 + 58*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 110*x^84 + 9*x^83 + 68*x^82 + 111*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 115*x^75 + 20*x^74 + 69*x^73 + 6*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 66*x^68 + 119*x^67 + 76*x^66 + 49*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 105*x^27 + 76*x^26 + 95*x^25 + 34*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 102*x^20 + 109*x^19 + 20*x^18 + 107*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 87*x^11 + 68*x^10 + x^9 + 14*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 90*x^4 + 43*x^3 + 28*x^2 + 93*x + 46, x^95 + 15*x^93 + 126*x^92 + 37*x^91 + 108*x^90 + 67*x^89 + 26*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 62*x^84 + 89*x^83 + 52*x^82 + 95*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 67*x^75 + 4*x^74 + 53*x^73 + 102*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 50*x^68 + 103*x^67 + 28*x^66 + x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 25*x^27 + 92*x^26 + 111*x^25 + 2*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 118*x^20 + 125*x^19 + 68*x^18 + 27*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 103*x^11 + 116*x^10 + 49*x^9 + 110*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 10*x^4 + 91*x^3 + 44*x^2 + 109*x + 110, x^95 + 15*x^93 + 102*x^92 + 69*x^91 + 44*x^90 + 67*x^89 + 2*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 70*x^84 + 57*x^83 + 52*x^82 + 95*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 35*x^75 + 68*x^74 + 53*x^73 + 62*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 42*x^68 + 7*x^67 + 28*x^66 + x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 57*x^27 + 28*x^26 + 111*x^25 + 10*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 30*x^20 + 93*x^19 + 68*x^18 + 27*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 71*x^11 + 52*x^10 + 49*x^9 + 102*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 34*x^4 + 123*x^3 + 44*x^2 + 109*x + 6, x^95 + 15*x^93 + 14*x^92 + 101*x^91 + 108*x^90 + 3*x^89 + 106*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 14*x^84 + 25*x^83 + 52*x^82 + 31*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 18*x^76 + 3*x^75 + 4*x^74 + 117*x^73 + 22*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 98*x^68 + 39*x^67 + 28*x^66 + 65*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 89*x^27 + 92*x^26 + 47*x^25 + 18*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 6*x^20 + 61*x^19 + 68*x^18 + 91*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 42*x^12 + 39*x^11 + 116*x^10 + 113*x^9 + 94*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 122*x^4 + 27*x^3 + 44*x^2 + 45*x + 30, x^95 + 15*x^93 + 86*x^92 + 5*x^91 + 76*x^90 + 3*x^89 + 18*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 54*x^84 + 121*x^83 + 20*x^82 + 31*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 99*x^75 + 36*x^74 + 117*x^73 + 46*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 58*x^68 + 71*x^67 + 60*x^66 + 65*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 121*x^27 + 60*x^26 + 47*x^25 + 90*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 78*x^20 + 29*x^19 + 36*x^18 + 91*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 7*x^11 + 20*x^10 + 113*x^9 + 22*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 114*x^4 + 59*x^3 + 76*x^2 + 45*x + 54, x^95 + 15*x^93 + 46*x^92 + 117*x^91 + 28*x^90 + 51*x^89 + 90*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 14*x^84 + 73*x^83 + 68*x^82 + 47*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 51*x^75 + 20*x^74 + 5*x^73 + 102*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 34*x^68 + 55*x^67 + 76*x^66 + 113*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 41*x^27 + 76*x^26 + 31*x^25 + 66*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 6*x^20 + 45*x^19 + 20*x^18 + 43*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 23*x^11 + 68*x^10 + 65*x^9 + 110*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 58*x^4 + 107*x^3 + 28*x^2 + 29*x + 14, x^95 + 15*x^93 + 54*x^92 + 69*x^91 + 44*x^90 + 67*x^89 + 18*x^88 + 117*x^87 + 56*x^86 + 11*x^85 + 86*x^84 + 57*x^83 + 52*x^82 + 95*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 42*x^76 + 35*x^75 + 68*x^74 + 53*x^73 + 46*x^72 + 107*x^71 + 88*x^70 + 53*x^69 + 26*x^68 + 7*x^67 + 28*x^66 + x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 120*x^58 + 30*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 72*x^50 + 86*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 72*x^42 + 74*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 120*x^34 + 66*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 57*x^27 + 28*x^26 + 111*x^25 + 90*x^24 + 9*x^23 + 88*x^22 + 119*x^21 + 110*x^20 + 93*x^19 + 68*x^18 + 27*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 98*x^12 + 71*x^11 + 52*x^10 + 49*x^9 + 22*x^8 + 15*x^7 + 56*x^6 + 17*x^5 + 82*x^4 + 123*x^3 + 44*x^2 + 109*x + 118, x^95 + 15*x^93 + 98*x^92 + 69*x^91 + 116*x^90 + 35*x^89 + 102*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 98*x^84 + 57*x^83 + 108*x^82 + 127*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 35*x^75 + 28*x^74 + 85*x^73 + 26*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 46*x^68 + 7*x^67 + 68*x^66 + 97*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 57*x^27 + 4*x^26 + 79*x^25 + 126*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 42*x^20 + 93*x^19 + 92*x^18 + 59*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 71*x^11 + 44*x^10 + 81*x^9 + 18*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 86*x^4 + 123*x^3 + 52*x^2 + 77*x + 82, x^95 + 15*x^93 + 106*x^92 + 5*x^91 + 84*x^90 + 67*x^89 + 78*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 74*x^84 + 121*x^83 + 76*x^82 + 95*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 99*x^75 + 60*x^74 + 53*x^73 + 114*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 70*x^68 + 71*x^67 + 100*x^66 + x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 121*x^27 + 100*x^26 + 111*x^25 + 6*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 50*x^20 + 29*x^19 + 60*x^18 + 27*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 7*x^11 + 76*x^10 + 49*x^9 + 10*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 14*x^4 + 59*x^3 + 84*x^2 + 109*x + 42, x^95 + 15*x^93 + 62*x^92 + 21*x^91 + 124*x^90 + 19*x^89 + 74*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 30*x^84 + 41*x^83 + 100*x^82 + 79*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 19*x^75 + 52*x^74 + 37*x^73 + 118*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 18*x^68 + 87*x^67 + 44*x^66 + 81*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 73*x^27 + 44*x^26 + 127*x^25 + 114*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 86*x^20 + 13*x^19 + 52*x^18 + 75*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 119*x^11 + 100*x^10 + 97*x^9 + 62*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 106*x^4 + 11*x^3 + 124*x^2 + 125*x + 94, x^95 + 15*x^93 + 70*x^92 + 53*x^91 + 124*x^90 + 19*x^89 + 18*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 70*x^84 + 9*x^83 + 36*x^82 + 79*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 90*x^76 + 115*x^75 + 52*x^74 + 37*x^73 + 110*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 106*x^68 + 119*x^67 + 108*x^66 + 81*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 105*x^27 + 44*x^26 + 127*x^25 + 90*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 30*x^20 + 109*x^19 + 116*x^18 + 75*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 82*x^12 + 87*x^11 + 100*x^10 + 97*x^9 + 86*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 98*x^4 + 43*x^3 + 60*x^2 + 125*x + 22, x^95 + 15*x^93 + 82*x^92 + 53*x^91 + 4*x^90 + 51*x^89 + 70*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 50*x^84 + 9*x^83 + 28*x^82 + 47*x^81 + 118*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 115*x^75 + 76*x^74 + 5*x^73 + 122*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 30*x^68 + 119*x^67 + 84*x^66 + 113*x^65 + 90*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 105*x^27 + 84*x^26 + 31*x^25 + 94*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 58*x^20 + 109*x^19 + 76*x^18 + 43*x^17 + 14*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 87*x^11 + 28*x^10 + 65*x^9 + 114*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 6*x^4 + 43*x^3 + 4*x^2 + 29*x + 18, x^95 + 15*x^93 + 102*x^92 + 37*x^91 + 76*x^90 + 35*x^89 + 34*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 6*x^84 + 89*x^83 + 20*x^82 + 127*x^81 + 50*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 67*x^75 + 36*x^74 + 85*x^73 + 30*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 106*x^68 + 103*x^67 + 60*x^66 + 97*x^65 + 62*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 25*x^27 + 60*x^26 + 79*x^25 + 42*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 94*x^20 + 125*x^19 + 36*x^18 + 59*x^17 + 58*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 103*x^11 + 20*x^10 + 81*x^9 + 70*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 98*x^4 + 91*x^3 + 76*x^2 + 77*x + 38, x^95 + 15*x^93 + 6*x^92 + 37*x^91 + 76*x^90 + 35*x^89 + 66*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 38*x^84 + 89*x^83 + 20*x^82 + 127*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 67*x^75 + 36*x^74 + 85*x^73 + 126*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 74*x^68 + 103*x^67 + 60*x^66 + 97*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 25*x^27 + 60*x^26 + 79*x^25 + 74*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 126*x^20 + 125*x^19 + 36*x^18 + 59*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 103*x^11 + 20*x^10 + 81*x^9 + 38*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 66*x^4 + 91*x^3 + 76*x^2 + 77*x + 6, x^95 + 15*x^93 + 66*x^92 + 21*x^91 + 68*x^90 + 83*x^89 + 54*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 98*x^84 + 41*x^83 + 92*x^82 + 15*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 19*x^75 + 12*x^74 + 101*x^73 + 10*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 110*x^68 + 87*x^67 + 20*x^66 + 17*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 73*x^27 + 20*x^26 + 63*x^25 + 14*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 42*x^20 + 13*x^19 + 12*x^18 + 11*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 119*x^11 + 92*x^10 + 33*x^9 + 66*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 22*x^4 + 11*x^3 + 68*x^2 + 61*x + 34, x^95 + 15*x^93 + 62*x^92 + 21*x^91 + 28*x^90 + 83*x^89 + 106*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 94*x^84 + 41*x^83 + 68*x^82 + 15*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 34*x^76 + 19*x^75 + 20*x^74 + 101*x^73 + 86*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 82*x^68 + 87*x^67 + 76*x^66 + 17*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 73*x^27 + 76*x^26 + 63*x^25 + 18*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 22*x^20 + 13*x^19 + 20*x^18 + 11*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 122*x^12 + 119*x^11 + 68*x^10 + 33*x^9 + 30*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 42*x^4 + 11*x^3 + 28*x^2 + 61*x + 126, x^95 + 15*x^93 + 14*x^92 + 117*x^91 + 60*x^90 + 51*x^89 + 26*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 46*x^84 + 73*x^83 + 36*x^82 + 47*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 82*x^76 + 51*x^75 + 116*x^74 + 5*x^73 + 38*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 2*x^68 + 55*x^67 + 108*x^66 + 113*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 70*x^28 + 41*x^27 + 108*x^26 + 31*x^25 + 2*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 38*x^20 + 45*x^19 + 116*x^18 + 43*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 106*x^12 + 23*x^11 + 36*x^10 + 65*x^9 + 46*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 26*x^4 + 107*x^3 + 60*x^2 + 29*x + 14, x^95 + 15*x^93 + 110*x^92 + 21*x^91 + 92*x^90 + 19*x^89 + 90*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 78*x^84 + 41*x^83 + 4*x^82 + 79*x^81 + 106*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 114*x^76 + 19*x^75 + 84*x^74 + 37*x^73 + 102*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 98*x^68 + 87*x^67 + 12*x^66 + 81*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 73*x^27 + 12*x^26 + 127*x^25 + 66*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 70*x^20 + 13*x^19 + 84*x^18 + 75*x^17 + 82*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 10*x^12 + 119*x^11 + 4*x^10 + 97*x^9 + 110*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 122*x^4 + 11*x^3 + 92*x^2 + 125*x + 14, x^95 + 15*x^93 + 66*x^92 + 85*x^91 + 100*x^90 + 83*x^89 + 86*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 34*x^84 + 105*x^83 + 60*x^82 + 15*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 83*x^75 + 108*x^74 + 101*x^73 + 106*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 46*x^68 + 23*x^67 + 52*x^66 + 17*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 9*x^27 + 52*x^26 + 63*x^25 + 46*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 106*x^20 + 77*x^19 + 108*x^18 + 11*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 55*x^11 + 60*x^10 + 33*x^9 + 34*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 86*x^4 + 75*x^3 + 100*x^2 + 61*x + 66, x^95 + 15*x^93 + 94*x^92 + 101*x^91 + 108*x^90 + 3*x^89 + 122*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 30*x^84 + 25*x^83 + 52*x^82 + 31*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 3*x^75 + 4*x^74 + 117*x^73 + 6*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 82*x^68 + 39*x^67 + 28*x^66 + 65*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 89*x^27 + 92*x^26 + 47*x^25 + 98*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 86*x^20 + 61*x^19 + 68*x^18 + 91*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 39*x^11 + 116*x^10 + 113*x^9 + 14*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 42*x^4 + 27*x^3 + 44*x^2 + 45*x + 14, x^95 + 15*x^93 + 18*x^92 + 101*x^91 + 116*x^90 + 3*x^89 + 86*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 82*x^84 + 25*x^83 + 108*x^82 + 31*x^81 + 38*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 3*x^75 + 28*x^74 + 117*x^73 + 42*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 62*x^68 + 39*x^67 + 68*x^66 + 65*x^65 + 106*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 89*x^27 + 4*x^26 + 47*x^25 + 46*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 90*x^20 + 61*x^19 + 92*x^18 + 91*x^17 + 126*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 39*x^11 + 44*x^10 + 113*x^9 + 98*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 38*x^4 + 27*x^3 + 52*x^2 + 45*x + 98, x^95 + 15*x^93 + 94*x^92 + 5*x^91 + 76*x^90 + 99*x^89 + 26*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 94*x^84 + 121*x^83 + 84*x^82 + 63*x^81 + 10*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 99*x^75 + 36*x^74 + 21*x^73 + 102*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 18*x^68 + 71*x^67 + 124*x^66 + 33*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 121*x^27 + 60*x^26 + 15*x^25 + 2*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 22*x^20 + 29*x^19 + 100*x^18 + 123*x^17 + 114*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 7*x^11 + 20*x^10 + 17*x^9 + 110*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 106*x^4 + 59*x^3 + 12*x^2 + 13*x + 46, x^95 + 15*x^93 + 74*x^92 + 5*x^91 + 20*x^90 + 67*x^89 + 110*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 42*x^84 + 121*x^83 + 12*x^82 + 95*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 99*x^75 + 124*x^74 + 53*x^73 + 82*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 102*x^68 + 71*x^67 + 36*x^66 + x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 121*x^27 + 36*x^26 + 111*x^25 + 38*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 18*x^20 + 29*x^19 + 124*x^18 + 27*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 7*x^11 + 12*x^10 + 49*x^9 + 106*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 46*x^4 + 59*x^3 + 20*x^2 + 109*x + 10, x^95 + 15*x^93 + 118*x^92 + 5*x^91 + 76*x^90 + 67*x^89 + 114*x^88 + 117*x^87 + 120*x^86 + 11*x^85 + 86*x^84 + 121*x^83 + 20*x^82 + 95*x^81 + 66*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 106*x^76 + 99*x^75 + 36*x^74 + 53*x^73 + 78*x^72 + 107*x^71 + 24*x^70 + 53*x^69 + 26*x^68 + 71*x^67 + 60*x^66 + x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 50*x^59 + 56*x^58 + 30*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 92*x^52 + 26*x^51 + 8*x^50 + 86*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 102*x^43 + 8*x^42 + 74*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 116*x^36 + 78*x^35 + 56*x^34 + 66*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 121*x^27 + 60*x^26 + 111*x^25 + 58*x^24 + 9*x^23 + 24*x^22 + 119*x^21 + 110*x^20 + 29*x^19 + 36*x^18 + 27*x^17 + 10*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 34*x^12 + 7*x^11 + 20*x^10 + 49*x^9 + 54*x^8 + 15*x^7 + 120*x^6 + 17*x^5 + 82*x^4 + 59*x^3 + 76*x^2 + 109*x + 86, x^95 + 15*x^93 + 94*x^92 + 53*x^91 + 60*x^90 + 115*x^89 + 42*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 62*x^84 + 9*x^83 + 36*x^82 + 111*x^81 + 58*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 115*x^75 + 116*x^74 + 69*x^73 + 22*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 114*x^68 + 119*x^67 + 108*x^66 + 49*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 105*x^27 + 108*x^26 + 95*x^25 + 82*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 118*x^20 + 109*x^19 + 116*x^18 + 107*x^17 + 98*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 87*x^11 + 36*x^10 + x^9 + 94*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 74*x^4 + 43*x^3 + 60*x^2 + 93*x + 126, x^95 + 15*x^93 + 30*x^92 + 117*x^91 + 60*x^90 + 51*x^89 + 106*x^88 + 21*x^87 + 88*x^86 + 43*x^85 + 126*x^84 + 73*x^83 + 36*x^82 + 47*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 66*x^76 + 51*x^75 + 116*x^74 + 5*x^73 + 86*x^72 + 11*x^71 + 120*x^70 + 85*x^69 + 50*x^68 + 55*x^67 + 108*x^66 + 113*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 24*x^58 + 126*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 40*x^50 + 118*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 40*x^42 + 106*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 24*x^34 + 34*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 41*x^27 + 108*x^26 + 31*x^25 + 18*x^24 + 41*x^23 + 120*x^22 + 23*x^21 + 54*x^20 + 45*x^19 + 116*x^18 + 43*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 26*x^12 + 23*x^11 + 36*x^10 + 65*x^9 + 30*x^8 + 47*x^7 + 88*x^6 + 49*x^5 + 10*x^4 + 107*x^3 + 60*x^2 + 29*x + 62, x^95 + 15*x^93 + 6*x^92 + 53*x^91 + 60*x^90 + 83*x^89 + 82*x^88 + 21*x^87 + 24*x^86 + 107*x^85 + 6*x^84 + 9*x^83 + 100*x^82 + 15*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 26*x^76 + 115*x^75 + 116*x^74 + 101*x^73 + 46*x^72 + 11*x^71 + 56*x^70 + 21*x^69 + 42*x^68 + 119*x^67 + 44*x^66 + 17*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 18*x^59 + 24*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 60*x^52 + 58*x^51 + 40*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 6*x^43 + 40*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 20*x^36 + 46*x^35 + 24*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 105*x^27 + 108*x^26 + 63*x^25 + 26*x^24 + 41*x^23 + 56*x^22 + 87*x^21 + 94*x^20 + 109*x^19 + 52*x^18 + 11*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 18*x^12 + 87*x^11 + 36*x^10 + 33*x^9 + 22*x^8 + 47*x^7 + 24*x^6 + 113*x^5 + 34*x^4 + 43*x^3 + 124*x^2 + 61*x + 86, x^95 + 15*x^93 + 66*x^92 + 5*x^91 + 84*x^90 + 35*x^89 + 38*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 2*x^84 + 121*x^83 + 12*x^82 + 127*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 99*x^75 + 60*x^74 + 85*x^73 + 90*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 14*x^68 + 71*x^67 + 36*x^66 + 97*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 121*x^27 + 100*x^26 + 79*x^25 + 62*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 74*x^20 + 29*x^19 + 124*x^18 + 59*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 7*x^11 + 76*x^10 + 81*x^9 + 82*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 54*x^4 + 59*x^3 + 20*x^2 + 77*x + 82, x^95 + 15*x^93 + 66*x^92 + 37*x^91 + 116*x^90 + 3*x^89 + 6*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 66*x^84 + 89*x^83 + 108*x^82 + 31*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 67*x^75 + 28*x^74 + 117*x^73 + 122*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 78*x^68 + 103*x^67 + 68*x^66 + 65*x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 25*x^27 + 4*x^26 + 47*x^25 + 30*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 10*x^20 + 125*x^19 + 92*x^18 + 91*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 103*x^11 + 44*x^10 + 113*x^9 + 114*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 118*x^4 + 91*x^3 + 52*x^2 + 45*x + 50, x^95 + 15*x^93 + 54*x^92 + 85*x^91 + 60*x^90 + 51*x^89 + 66*x^88 + 85*x^87 + 24*x^86 + 43*x^85 + 118*x^84 + 105*x^83 + 100*x^82 + 47*x^81 + 50*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 83*x^75 + 116*x^74 + 5*x^73 + 62*x^72 + 75*x^71 + 56*x^70 + 85*x^69 + 58*x^68 + 23*x^67 + 44*x^66 + 113*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 24*x^58 + 126*x^57 + 84*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 40*x^50 + 118*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 40*x^42 + 106*x^41 + 124*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 24*x^34 + 34*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 9*x^27 + 108*x^26 + 31*x^25 + 74*x^24 + 105*x^23 + 56*x^22 + 23*x^21 + 14*x^20 + 77*x^19 + 52*x^18 + 43*x^17 + 58*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 55*x^11 + 36*x^10 + 65*x^9 + 102*x^8 + 111*x^7 + 24*x^6 + 49*x^5 + 114*x^4 + 75*x^3 + 124*x^2 + 29*x + 102, x^95 + 15*x^93 + 78*x^92 + 69*x^91 + 44*x^90 + 99*x^89 + 42*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 78*x^84 + 57*x^83 + 116*x^82 + 63*x^81 + 26*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 35*x^75 + 68*x^74 + 21*x^73 + 86*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 34*x^68 + 7*x^67 + 92*x^66 + 33*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 57*x^27 + 28*x^26 + 15*x^25 + 82*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 70*x^20 + 93*x^19 + 4*x^18 + 123*x^17 + 66*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 71*x^11 + 52*x^10 + 17*x^9 + 30*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 58*x^4 + 123*x^3 + 108*x^2 + 13*x + 94, x^95 + 15*x^93 + 74*x^92 + 117*x^91 + 100*x^90 + 83*x^89 + 94*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 74*x^84 + 73*x^83 + 124*x^82 + 15*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 51*x^75 + 108*x^74 + 101*x^73 + 34*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 6*x^68 + 55*x^67 + 116*x^66 + 17*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 41*x^27 + 52*x^26 + 63*x^25 + 86*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 50*x^20 + 45*x^19 + 44*x^18 + 11*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 23*x^11 + 60*x^10 + 33*x^9 + 122*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 78*x^4 + 107*x^3 + 36*x^2 + 61*x + 58, x^95 + 15*x^93 + 10*x^92 + 85*x^91 + 36*x^90 + 51*x^89 + 30*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 10*x^84 + 105*x^83 + 60*x^82 + 47*x^81 + 110*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 83*x^75 + 44*x^74 + 5*x^73 + 98*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 70*x^68 + 23*x^67 + 52*x^66 + 113*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 9*x^27 + 116*x^26 + 31*x^25 + 22*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 114*x^20 + 77*x^19 + 108*x^18 + 43*x^17 + 102*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 55*x^11 + 124*x^10 + 65*x^9 + 58*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 14*x^4 + 75*x^3 + 100*x^2 + 29*x + 122, x^95 + 15*x^93 + 118*x^92 + 85*x^91 + 28*x^90 + 51*x^89 + 34*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 118*x^84 + 105*x^83 + 4*x^82 + 47*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 83*x^75 + 20*x^74 + 5*x^73 + 94*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 58*x^68 + 23*x^67 + 12*x^66 + 113*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 9*x^27 + 76*x^26 + 31*x^25 + 42*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 14*x^20 + 77*x^19 + 84*x^18 + 43*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 55*x^11 + 68*x^10 + 65*x^9 + 6*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 114*x^4 + 75*x^3 + 92*x^2 + 29*x + 70, x^95 + 15*x^93 + 98*x^92 + 37*x^91 + 20*x^90 + 3*x^89 + 6*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 34*x^84 + 89*x^83 + 76*x^82 + 31*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 126*x^76 + 67*x^75 + 124*x^74 + 117*x^73 + 122*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 110*x^68 + 103*x^67 + 100*x^66 + 65*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 84*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 28*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 25*x^27 + 36*x^26 + 47*x^25 + 30*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 106*x^20 + 125*x^19 + 60*x^18 + 91*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 38*x^12 + 103*x^11 + 12*x^10 + 113*x^9 + 114*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 22*x^4 + 91*x^3 + 84*x^2 + 45*x + 114, x^95 + 15*x^93 + 42*x^92 + 69*x^91 + 116*x^90 + 67*x^89 + 46*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 74*x^84 + 57*x^83 + 44*x^82 + 95*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 35*x^75 + 28*x^74 + 53*x^73 + 18*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 70*x^68 + 7*x^67 + 4*x^66 + x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 57*x^27 + 4*x^26 + 111*x^25 + 102*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 50*x^20 + 93*x^19 + 28*x^18 + 27*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 71*x^11 + 44*x^10 + 49*x^9 + 42*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 14*x^4 + 123*x^3 + 116*x^2 + 109*x + 10, x^95 + 15*x^93 + 42*x^92 + 69*x^91 + 20*x^90 + 67*x^89 + 14*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 10*x^84 + 57*x^83 + 12*x^82 + 95*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 35*x^75 + 124*x^74 + 53*x^73 + 50*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 6*x^68 + 7*x^67 + 36*x^66 + x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 57*x^27 + 36*x^26 + 111*x^25 + 70*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 114*x^20 + 93*x^19 + 124*x^18 + 27*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 71*x^11 + 12*x^10 + 49*x^9 + 74*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 78*x^4 + 123*x^3 + 20*x^2 + 109*x + 106, x^95 + 15*x^93 + 110*x^92 + 69*x^91 + 108*x^90 + 35*x^89 + 74*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 110*x^84 + 57*x^83 + 52*x^82 + 127*x^81 + 58*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 35*x^75 + 4*x^74 + 85*x^73 + 54*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 2*x^68 + 7*x^67 + 28*x^66 + 97*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 57*x^27 + 92*x^26 + 79*x^25 + 114*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 102*x^20 + 93*x^19 + 68*x^18 + 59*x^17 + 98*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 71*x^11 + 116*x^10 + 81*x^9 + 126*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 26*x^4 + 123*x^3 + 44*x^2 + 77*x + 62, x^95 + 15*x^93 + 42*x^92 + 69*x^91 + 84*x^90 + 3*x^89 + 14*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 10*x^84 + 57*x^83 + 76*x^82 + 31*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 118*x^76 + 35*x^75 + 60*x^74 + 117*x^73 + 50*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 6*x^68 + 7*x^67 + 100*x^66 + 65*x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 82*x^28 + 57*x^27 + 100*x^26 + 47*x^25 + 70*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 114*x^20 + 93*x^19 + 60*x^18 + 91*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 62*x^12 + 71*x^11 + 76*x^10 + 113*x^9 + 74*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 78*x^4 + 123*x^3 + 84*x^2 + 45*x + 106, x^95 + 15*x^93 + 10*x^92 + 53*x^91 + 36*x^90 + 19*x^89 + 94*x^88 + 21*x^87 + 40*x^86 + 107*x^85 + 10*x^84 + 9*x^83 + 60*x^82 + 79*x^81 + 46*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 115*x^75 + 44*x^74 + 37*x^73 + 34*x^72 + 11*x^71 + 8*x^70 + 21*x^69 + 70*x^68 + 119*x^67 + 52*x^66 + 81*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 40*x^58 + 62*x^57 + 108*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 24*x^50 + 54*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 24*x^42 + 42*x^41 + 68*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 40*x^34 + 98*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 105*x^27 + 116*x^26 + 127*x^25 + 86*x^24 + 41*x^23 + 8*x^22 + 87*x^21 + 114*x^20 + 109*x^19 + 108*x^18 + 75*x^17 + 38*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 87*x^11 + 124*x^10 + 97*x^9 + 122*x^8 + 47*x^7 + 40*x^6 + 113*x^5 + 14*x^4 + 43*x^3 + 100*x^2 + 125*x + 58, x^95 + 15*x^93 + 106*x^92 + 5*x^91 + 20*x^90 + 67*x^89 + 14*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 74*x^84 + 121*x^83 + 12*x^82 + 95*x^81 + 126*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 54*x^76 + 99*x^75 + 124*x^74 + 53*x^73 + 50*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 70*x^68 + 71*x^67 + 36*x^66 + x^65 + 18*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 100*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 76*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 121*x^27 + 36*x^26 + 111*x^25 + 70*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 50*x^20 + 29*x^19 + 124*x^18 + 27*x^17 + 54*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 126*x^12 + 7*x^11 + 12*x^10 + 49*x^9 + 74*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 14*x^4 + 59*x^3 + 20*x^2 + 109*x + 106, x^95 + 15*x^93 + 66*x^92 + 101*x^91 + 116*x^90 + 67*x^89 + 6*x^88 + 53*x^87 + 72*x^86 + 11*x^85 + 66*x^84 + 25*x^83 + 108*x^82 + 95*x^81 + 22*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 3*x^75 + 28*x^74 + 53*x^73 + 122*x^72 + 43*x^71 + 40*x^70 + 53*x^69 + 78*x^68 + 39*x^67 + 68*x^66 + x^65 + 122*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 114*x^59 + 72*x^58 + 30*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 90*x^51 + 120*x^50 + 86*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 38*x^43 + 120*x^42 + 74*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 14*x^35 + 72*x^34 + 66*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 89*x^27 + 4*x^26 + 111*x^25 + 30*x^24 + 73*x^23 + 40*x^22 + 119*x^21 + 10*x^20 + 61*x^19 + 92*x^18 + 27*x^17 + 46*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 39*x^11 + 44*x^10 + 49*x^9 + 114*x^8 + 79*x^7 + 72*x^6 + 17*x^5 + 118*x^4 + 27*x^3 + 52*x^2 + 109*x + 50, x^95 + 15*x^93 + 2*x^92 + 69*x^91 + 20*x^90 + 99*x^89 + 38*x^88 + 117*x^87 + 8*x^86 + 75*x^85 + 66*x^84 + 57*x^83 + 76*x^82 + 63*x^81 + 118*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 94*x^76 + 35*x^75 + 124*x^74 + 21*x^73 + 90*x^72 + 107*x^71 + 104*x^70 + 117*x^69 + 78*x^68 + 7*x^67 + 100*x^66 + 33*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 8*x^58 + 94*x^57 + 60*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 56*x^50 + 22*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 56*x^42 + 10*x^41 + 52*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 8*x^34 + 2*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 57*x^27 + 36*x^26 + 15*x^25 + 62*x^24 + 9*x^23 + 104*x^22 + 55*x^21 + 10*x^20 + 93*x^19 + 60*x^18 + 123*x^17 + 14*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 6*x^12 + 71*x^11 + 12*x^10 + 17*x^9 + 82*x^8 + 15*x^7 + 8*x^6 + 81*x^5 + 118*x^4 + 123*x^3 + 84*x^2 + 13*x + 82, x^95 + 15*x^93 + 66*x^92 + 5*x^91 + 116*x^90 + 99*x^89 + 70*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 66*x^84 + 121*x^83 + 108*x^82 + 63*x^81 + 86*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 30*x^76 + 99*x^75 + 28*x^74 + 21*x^73 + 58*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 78*x^68 + 71*x^67 + 68*x^66 + 33*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 124*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 20*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 116*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 92*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 121*x^27 + 4*x^26 + 15*x^25 + 94*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 10*x^20 + 29*x^19 + 92*x^18 + 123*x^17 + 110*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 70*x^12 + 7*x^11 + 44*x^10 + 17*x^9 + 50*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 118*x^4 + 59*x^3 + 52*x^2 + 13*x + 114, x^95 + 15*x^93 + 30*x^92 + 5*x^91 + 108*x^90 + 35*x^89 + 122*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 94*x^84 + 121*x^83 + 52*x^82 + 127*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 99*x^75 + 4*x^74 + 85*x^73 + 6*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 18*x^68 + 71*x^67 + 28*x^66 + 97*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 121*x^27 + 92*x^26 + 79*x^25 + 98*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 22*x^20 + 29*x^19 + 68*x^18 + 59*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 7*x^11 + 116*x^10 + 81*x^9 + 14*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 106*x^4 + 59*x^3 + 44*x^2 + 77*x + 14, x^95 + 15*x^93 + 6*x^92 + 101*x^91 + 44*x^90 + 35*x^89 + 34*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 102*x^84 + 25*x^83 + 52*x^82 + 127*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 90*x^76 + 3*x^75 + 68*x^74 + 85*x^73 + 30*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 10*x^68 + 39*x^67 + 28*x^66 + 97*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 30*x^28 + 89*x^27 + 28*x^26 + 79*x^25 + 42*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 62*x^20 + 61*x^19 + 68*x^18 + 59*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 82*x^12 + 39*x^11 + 52*x^10 + 81*x^9 + 70*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 2*x^4 + 27*x^3 + 44*x^2 + 77*x + 102, x^95 + 15*x^93 + 122*x^92 + 101*x^91 + 52*x^90 + 99*x^89 + 62*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 90*x^84 + 25*x^83 + 108*x^82 + 63*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 3*x^75 + 92*x^74 + 21*x^73 + 2*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 54*x^68 + 39*x^67 + 68*x^66 + 33*x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 89*x^27 + 68*x^26 + 15*x^25 + 54*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 2*x^20 + 61*x^19 + 92*x^18 + 123*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 39*x^11 + 108*x^10 + 17*x^9 + 90*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 62*x^4 + 27*x^3 + 52*x^2 + 13*x + 122, x^95 + 15*x^93 + 74*x^92 + 85*x^91 + 4*x^90 + 51*x^89 + 126*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 10*x^84 + 105*x^83 + 92*x^82 + 47*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 83*x^75 + 76*x^74 + 5*x^73 + 2*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 70*x^68 + 23*x^67 + 20*x^66 + 113*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 9*x^27 + 84*x^26 + 31*x^25 + 118*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 114*x^20 + 77*x^19 + 12*x^18 + 43*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 55*x^11 + 28*x^10 + 65*x^9 + 90*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 14*x^4 + 75*x^3 + 68*x^2 + 29*x + 90, x^95 + 15*x^93 + 18*x^92 + 37*x^91 + 20*x^90 + 67*x^89 + 54*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 18*x^84 + 89*x^83 + 76*x^82 + 95*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 78*x^76 + 67*x^75 + 124*x^74 + 53*x^73 + 74*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 126*x^68 + 103*x^67 + 100*x^66 + x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 52*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 60*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 90*x^28 + 25*x^27 + 36*x^26 + 111*x^25 + 14*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 26*x^20 + 125*x^19 + 60*x^18 + 27*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 54*x^12 + 103*x^11 + 12*x^10 + 49*x^9 + 2*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 102*x^4 + 91*x^3 + 84*x^2 + 109*x + 66, x^95 + 15*x^93 + 126*x^92 + 69*x^91 + 12*x^90 + 99*x^89 + 58*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 126*x^84 + 57*x^83 + 20*x^82 + 63*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 34*x^76 + 35*x^75 + 100*x^74 + 21*x^73 + 70*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 114*x^68 + 7*x^67 + 60*x^66 + 33*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 57*x^27 + 124*x^26 + 15*x^25 + 34*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 54*x^20 + 93*x^19 + 36*x^18 + 123*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 122*x^12 + 71*x^11 + 84*x^10 + 17*x^9 + 78*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 74*x^4 + 123*x^3 + 76*x^2 + 13*x + 14, x^95 + 15*x^93 + 98*x^92 + 85*x^91 + 68*x^90 + 83*x^89 + 22*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 2*x^84 + 105*x^83 + 92*x^82 + 15*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 83*x^75 + 12*x^74 + 101*x^73 + 42*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 78*x^68 + 23*x^67 + 20*x^66 + 17*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 9*x^27 + 20*x^26 + 63*x^25 + 110*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 74*x^20 + 77*x^19 + 12*x^18 + 11*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 55*x^11 + 92*x^10 + 33*x^9 + 98*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 118*x^4 + 75*x^3 + 68*x^2 + 61*x + 66, x^95 + 15*x^93 + 106*x^92 + 21*x^91 + 36*x^90 + 115*x^89 + 126*x^88 + 85*x^87 + 40*x^86 + 43*x^85 + 106*x^84 + 41*x^83 + 60*x^82 + 111*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 118*x^76 + 19*x^75 + 44*x^74 + 69*x^73 + 2*x^72 + 75*x^71 + 8*x^70 + 85*x^69 + 102*x^68 + 87*x^67 + 52*x^66 + 49*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 100*x^60 + 82*x^59 + 40*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 36*x^52 + 122*x^51 + 24*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 108*x^44 + 70*x^43 + 24*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 12*x^36 + 110*x^35 + 40*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 18*x^28 + 73*x^27 + 116*x^26 + 95*x^25 + 118*x^24 + 105*x^23 + 8*x^22 + 23*x^21 + 82*x^20 + 13*x^19 + 108*x^18 + 107*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 62*x^12 + 119*x^11 + 124*x^10 + x^9 + 90*x^8 + 111*x^7 + 40*x^6 + 49*x^5 + 46*x^4 + 11*x^3 + 100*x^2 + 93*x + 26, x^95 + 15*x^93 + 122*x^92 + 5*x^91 + 52*x^90 + 67*x^89 + 62*x^88 + 117*x^87 + 8*x^86 + 11*x^85 + 90*x^84 + 121*x^83 + 108*x^82 + 95*x^81 + 46*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 99*x^75 + 92*x^74 + 53*x^73 + 2*x^72 + 107*x^71 + 104*x^70 + 53*x^69 + 54*x^68 + 71*x^67 + 68*x^66 + x^65 + 98*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 72*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 120*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 120*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 72*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 121*x^27 + 68*x^26 + 111*x^25 + 54*x^24 + 9*x^23 + 104*x^22 + 119*x^21 + 2*x^20 + 29*x^19 + 92*x^18 + 27*x^17 + 38*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 7*x^11 + 108*x^10 + 49*x^9 + 90*x^8 + 15*x^7 + 8*x^6 + 17*x^5 + 62*x^4 + 59*x^3 + 52*x^2 + 109*x + 122, x^95 + 15*x^93 + 66*x^92 + 53*x^91 + 4*x^90 + 115*x^89 + 54*x^88 + 21*x^87 + 40*x^86 + 43*x^85 + 98*x^84 + 9*x^83 + 28*x^82 + 111*x^81 + 38*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 94*x^76 + 115*x^75 + 76*x^74 + 69*x^73 + 10*x^72 + 11*x^71 + 8*x^70 + 85*x^69 + 110*x^68 + 119*x^67 + 84*x^66 + 49*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 104*x^58 + 126*x^57 + 92*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 88*x^50 + 118*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 88*x^42 + 106*x^41 + 20*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 104*x^34 + 34*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 74*x^28 + 105*x^27 + 84*x^26 + 95*x^25 + 14*x^24 + 41*x^23 + 8*x^22 + 23*x^21 + 42*x^20 + 109*x^19 + 76*x^18 + 107*x^17 + 126*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 6*x^12 + 87*x^11 + 28*x^10 + x^9 + 66*x^8 + 47*x^7 + 40*x^6 + 49*x^5 + 22*x^4 + 43*x^3 + 4*x^2 + 93*x + 34, x^95 + 15*x^93 + 118*x^92 + 117*x^91 + 92*x^90 + 83*x^89 + 34*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 118*x^84 + 73*x^83 + 68*x^82 + 15*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 51*x^75 + 84*x^74 + 101*x^73 + 94*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 58*x^68 + 55*x^67 + 76*x^66 + 17*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 41*x^27 + 12*x^26 + 63*x^25 + 42*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 14*x^20 + 45*x^19 + 20*x^18 + 11*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 23*x^11 + 4*x^10 + 33*x^9 + 6*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 114*x^4 + 107*x^3 + 28*x^2 + 61*x + 70, x^95 + 15*x^93 + 38*x^92 + 101*x^91 + 44*x^90 + 35*x^89 + 66*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 6*x^84 + 25*x^83 + 52*x^82 + 127*x^81 + 18*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 58*x^76 + 3*x^75 + 68*x^74 + 85*x^73 + 126*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 106*x^68 + 39*x^67 + 28*x^66 + 97*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 89*x^27 + 28*x^26 + 79*x^25 + 74*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 94*x^20 + 61*x^19 + 68*x^18 + 59*x^17 + 26*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 50*x^12 + 39*x^11 + 52*x^10 + 81*x^9 + 38*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 98*x^4 + 27*x^3 + 44*x^2 + 77*x + 70, x^95 + 15*x^93 + 50*x^92 + 37*x^91 + 84*x^90 + 3*x^89 + 86*x^88 + 53*x^87 + 8*x^86 + 11*x^85 + 50*x^84 + 89*x^83 + 12*x^82 + 31*x^81 + 102*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 46*x^76 + 67*x^75 + 60*x^74 + 117*x^73 + 42*x^72 + 43*x^71 + 104*x^70 + 53*x^69 + 94*x^68 + 103*x^67 + 36*x^66 + 65*x^65 + 42*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 114*x^59 + 8*x^58 + 30*x^57 + 28*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 90*x^51 + 56*x^50 + 86*x^49 + 124*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 38*x^43 + 56*x^42 + 74*x^41 + 84*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 14*x^35 + 8*x^34 + 66*x^33 + 20*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 25*x^27 + 100*x^26 + 47*x^25 + 46*x^24 + 73*x^23 + 104*x^22 + 119*x^21 + 58*x^20 + 125*x^19 + 124*x^18 + 91*x^17 + 62*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 22*x^12 + 103*x^11 + 76*x^10 + 113*x^9 + 98*x^8 + 79*x^7 + 8*x^6 + 17*x^5 + 70*x^4 + 91*x^3 + 20*x^2 + 45*x + 34, x^95 + 15*x^93 + 78*x^92 + 53*x^91 + 92*x^90 + 115*x^89 + 58*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 46*x^84 + 9*x^83 + 4*x^82 + 111*x^81 + 74*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 18*x^76 + 115*x^75 + 84*x^74 + 69*x^73 + 6*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 2*x^68 + 119*x^67 + 12*x^66 + 49*x^65 + 102*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 76*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 68*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 105*x^27 + 12*x^26 + 95*x^25 + 34*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 38*x^20 + 109*x^19 + 84*x^18 + 107*x^17 + 50*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 42*x^12 + 87*x^11 + 4*x^10 + x^9 + 14*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 26*x^4 + 43*x^3 + 92*x^2 + 93*x + 46, x^95 + 15*x^93 + 10*x^92 + 69*x^91 + 20*x^90 + 67*x^89 + 110*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 106*x^84 + 57*x^83 + 12*x^82 + 95*x^81 + 94*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 35*x^75 + 124*x^74 + 53*x^73 + 82*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 38*x^68 + 7*x^67 + 36*x^66 + x^65 + 50*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 57*x^27 + 36*x^26 + 111*x^25 + 38*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 82*x^20 + 93*x^19 + 124*x^18 + 27*x^17 + 22*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 71*x^11 + 12*x^10 + 49*x^9 + 106*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 110*x^4 + 123*x^3 + 20*x^2 + 109*x + 10, x^95 + 15*x^93 + 62*x^92 + 69*x^91 + 108*x^90 + 99*x^89 + 26*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 126*x^84 + 57*x^83 + 52*x^82 + 63*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 98*x^76 + 35*x^75 + 4*x^74 + 21*x^73 + 102*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 114*x^68 + 7*x^67 + 28*x^66 + 33*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 108*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 36*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 54*x^28 + 57*x^27 + 92*x^26 + 15*x^25 + 2*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 54*x^20 + 93*x^19 + 68*x^18 + 123*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 58*x^12 + 71*x^11 + 116*x^10 + 17*x^9 + 110*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 74*x^4 + 123*x^3 + 44*x^2 + 13*x + 110, x^95 + 15*x^93 + 30*x^92 + 5*x^91 + 44*x^90 + 99*x^89 + 122*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 94*x^84 + 121*x^83 + 116*x^82 + 63*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 99*x^75 + 68*x^74 + 21*x^73 + 6*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 18*x^68 + 71*x^67 + 92*x^66 + 33*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 121*x^27 + 28*x^26 + 15*x^25 + 98*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 22*x^20 + 29*x^19 + 4*x^18 + 123*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 7*x^11 + 52*x^10 + 17*x^9 + 14*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 106*x^4 + 59*x^3 + 108*x^2 + 13*x + 14, x^95 + 15*x^93 + 46*x^92 + 85*x^91 + 124*x^90 + 19*x^89 + 58*x^88 + 85*x^87 + 88*x^86 + 107*x^85 + 78*x^84 + 105*x^83 + 100*x^82 + 79*x^81 + 10*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 83*x^75 + 52*x^74 + 37*x^73 + 6*x^72 + 75*x^71 + 120*x^70 + 21*x^69 + 98*x^68 + 23*x^67 + 44*x^66 + 81*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 82*x^59 + 24*x^58 + 62*x^57 + 4*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 122*x^51 + 40*x^50 + 54*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 70*x^43 + 40*x^42 + 42*x^41 + 12*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 110*x^35 + 24*x^34 + 98*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 9*x^27 + 44*x^26 + 127*x^25 + 34*x^24 + 105*x^23 + 120*x^22 + 87*x^21 + 70*x^20 + 77*x^19 + 52*x^18 + 75*x^17 + 114*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 55*x^11 + 100*x^10 + 97*x^9 + 14*x^8 + 111*x^7 + 88*x^6 + 113*x^5 + 122*x^4 + 75*x^3 + 124*x^2 + 125*x + 110, x^95 + 15*x^93 + 50*x^92 + 21*x^91 + 4*x^90 + 19*x^89 + 102*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 18*x^84 + 41*x^83 + 28*x^82 + 79*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 19*x^75 + 76*x^74 + 37*x^73 + 90*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 62*x^68 + 87*x^67 + 84*x^66 + 81*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 73*x^27 + 84*x^26 + 127*x^25 + 126*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 26*x^20 + 13*x^19 + 76*x^18 + 75*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 119*x^11 + 28*x^10 + 97*x^9 + 82*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 38*x^4 + 11*x^3 + 4*x^2 + 125*x + 114, x^95 + 15*x^93 + 90*x^92 + 69*x^91 + 20*x^90 + 3*x^89 + 62*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 122*x^84 + 57*x^83 + 12*x^82 + 31*x^81 + 110*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 70*x^76 + 35*x^75 + 124*x^74 + 117*x^73 + 2*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 22*x^68 + 7*x^67 + 36*x^66 + 65*x^65 + 34*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 68*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 44*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 68*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 76*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 12*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 4*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 108*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 4*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 66*x^28 + 57*x^27 + 36*x^26 + 47*x^25 + 54*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 34*x^20 + 93*x^19 + 124*x^18 + 91*x^17 + 102*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 78*x^12 + 71*x^11 + 12*x^10 + 113*x^9 + 90*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 30*x^4 + 123*x^3 + 20*x^2 + 45*x + 58, x^95 + 15*x^93 + 78*x^92 + 69*x^91 + 44*x^90 + 35*x^89 + 106*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 78*x^84 + 57*x^83 + 116*x^82 + 127*x^81 + 90*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 35*x^75 + 68*x^74 + 85*x^73 + 22*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 34*x^68 + 7*x^67 + 92*x^66 + 97*x^65 + 22*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 100*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 44*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 57*x^27 + 28*x^26 + 79*x^25 + 18*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 70*x^20 + 93*x^19 + 4*x^18 + 59*x^17 + 2*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 71*x^11 + 52*x^10 + 81*x^9 + 94*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 58*x^4 + 123*x^3 + 108*x^2 + 77*x + 30, x^95 + 15*x^93 + 118*x^92 + 85*x^91 + 28*x^90 + 115*x^89 + 98*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 118*x^84 + 105*x^83 + 4*x^82 + 111*x^81 + 18*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 42*x^76 + 83*x^75 + 20*x^74 + 69*x^73 + 30*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 58*x^68 + 23*x^67 + 12*x^66 + 49*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 78*x^28 + 9*x^27 + 76*x^26 + 95*x^25 + 106*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 14*x^20 + 77*x^19 + 84*x^18 + 107*x^17 + 26*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 98*x^12 + 55*x^11 + 68*x^10 + x^9 + 70*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 114*x^4 + 75*x^3 + 92*x^2 + 93*x + 6, x^95 + 15*x^93 + 126*x^92 + 85*x^91 + 92*x^90 + 83*x^89 + 42*x^88 + 85*x^87 + 24*x^86 + 107*x^85 + 30*x^84 + 105*x^83 + 4*x^82 + 15*x^81 + 122*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 98*x^76 + 83*x^75 + 84*x^74 + 101*x^73 + 22*x^72 + 75*x^71 + 56*x^70 + 21*x^69 + 18*x^68 + 23*x^67 + 12*x^66 + 17*x^65 + 54*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 44*x^60 + 82*x^59 + 88*x^58 + 62*x^57 + 100*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 44*x^52 + 122*x^51 + 104*x^50 + 54*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 68*x^44 + 70*x^43 + 104*x^42 + 42*x^41 + 44*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 100*x^36 + 110*x^35 + 88*x^34 + 98*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 118*x^28 + 9*x^27 + 12*x^26 + 63*x^25 + 82*x^24 + 105*x^23 + 56*x^22 + 87*x^21 + 86*x^20 + 77*x^19 + 84*x^18 + 11*x^17 + 34*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 58*x^12 + 55*x^11 + 4*x^10 + 33*x^9 + 94*x^8 + 111*x^7 + 24*x^6 + 113*x^5 + 106*x^4 + 75*x^3 + 92*x^2 + 61*x + 62, x^95 + 15*x^93 + 98*x^92 + 21*x^91 + 68*x^90 + 19*x^89 + 22*x^88 + 85*x^87 + 40*x^86 + 107*x^85 + 2*x^84 + 41*x^83 + 92*x^82 + 79*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 62*x^76 + 19*x^75 + 12*x^74 + 37*x^73 + 42*x^72 + 75*x^71 + 8*x^70 + 21*x^69 + 78*x^68 + 87*x^67 + 20*x^66 + 81*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 20*x^60 + 82*x^59 + 104*x^58 + 62*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 20*x^52 + 122*x^51 + 88*x^50 + 54*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 124*x^44 + 70*x^43 + 88*x^42 + 42*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 92*x^36 + 110*x^35 + 104*x^34 + 98*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 106*x^28 + 73*x^27 + 20*x^26 + 127*x^25 + 110*x^24 + 105*x^23 + 8*x^22 + 87*x^21 + 74*x^20 + 13*x^19 + 12*x^18 + 75*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 102*x^12 + 119*x^11 + 92*x^10 + 97*x^9 + 98*x^8 + 111*x^7 + 40*x^6 + 113*x^5 + 118*x^4 + 11*x^3 + 68*x^2 + 125*x + 66, x^95 + 15*x^93 + 94*x^92 + 53*x^91 + 92*x^90 + 115*x^89 + 10*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 126*x^84 + 9*x^83 + 4*x^82 + 111*x^81 + 90*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 2*x^76 + 115*x^75 + 84*x^74 + 69*x^73 + 54*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 50*x^68 + 119*x^67 + 12*x^66 + 49*x^65 + 86*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 36*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 108*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 4*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 108*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 36*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 108*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 105*x^27 + 12*x^26 + 95*x^25 + 50*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 54*x^20 + 109*x^19 + 84*x^18 + 107*x^17 + 2*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 90*x^12 + 87*x^11 + 4*x^10 + x^9 + 126*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 10*x^4 + 43*x^3 + 92*x^2 + 93*x + 94, x^95 + 15*x^93 + 58*x^92 + 101*x^91 + 20*x^90 + 99*x^89 + 30*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 90*x^84 + 25*x^83 + 12*x^82 + 63*x^81 + 78*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 102*x^76 + 3*x^75 + 124*x^74 + 21*x^73 + 34*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 54*x^68 + 39*x^67 + 36*x^66 + 33*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 34*x^28 + 89*x^27 + 36*x^26 + 15*x^25 + 22*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 2*x^20 + 61*x^19 + 124*x^18 + 123*x^17 + 70*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 110*x^12 + 39*x^11 + 12*x^10 + 17*x^9 + 122*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 62*x^4 + 27*x^3 + 20*x^2 + 13*x + 90, x^95 + 15*x^93 + 22*x^92 + 101*x^91 + 12*x^90 + 35*x^89 + 18*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 118*x^84 + 25*x^83 + 84*x^82 + 127*x^81 + 98*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 3*x^75 + 100*x^74 + 85*x^73 + 46*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 122*x^68 + 39*x^67 + 124*x^66 + 97*x^65 + 14*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 89*x^27 + 124*x^26 + 79*x^25 + 90*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 14*x^20 + 61*x^19 + 100*x^18 + 59*x^17 + 42*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 39*x^11 + 84*x^10 + 81*x^9 + 22*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 50*x^4 + 27*x^3 + 12*x^2 + 77*x + 54, x^95 + 15*x^93 + 86*x^92 + 101*x^91 + 12*x^90 + 35*x^89 + 82*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 54*x^84 + 25*x^83 + 84*x^82 + 127*x^81 + 34*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 10*x^76 + 3*x^75 + 100*x^74 + 85*x^73 + 110*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 58*x^68 + 39*x^67 + 124*x^66 + 97*x^65 + 78*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 116*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 84*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 92*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 92*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 46*x^28 + 89*x^27 + 124*x^26 + 79*x^25 + 26*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 78*x^20 + 61*x^19 + 100*x^18 + 59*x^17 + 106*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 66*x^12 + 39*x^11 + 84*x^10 + 81*x^9 + 86*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 114*x^4 + 27*x^3 + 12*x^2 + 77*x + 118, x^95 + 15*x^93 + 102*x^92 + 101*x^91 + 76*x^90 + 35*x^89 + 98*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 6*x^84 + 25*x^83 + 20*x^82 + 127*x^81 + 114*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 122*x^76 + 3*x^75 + 36*x^74 + 85*x^73 + 94*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 106*x^68 + 39*x^67 + 60*x^66 + 97*x^65 + 126*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 20*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 60*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 116*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 60*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 20*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 60*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 89*x^27 + 60*x^26 + 79*x^25 + 106*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 94*x^20 + 61*x^19 + 36*x^18 + 59*x^17 + 122*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 114*x^12 + 39*x^11 + 20*x^10 + 81*x^9 + 6*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 98*x^4 + 27*x^3 + 76*x^2 + 77*x + 102, x^95 + 15*x^93 + 82*x^92 + 117*x^91 + 36*x^90 + 115*x^89 + 38*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 114*x^84 + 73*x^83 + 124*x^82 + 111*x^81 + 22*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 78*x^76 + 51*x^75 + 44*x^74 + 69*x^73 + 26*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 94*x^68 + 55*x^67 + 116*x^66 + 49*x^65 + 58*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 116*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 60*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 116*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 92*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 28*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 52*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 124*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 52*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 26*x^28 + 41*x^27 + 116*x^26 + 95*x^25 + 62*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 122*x^20 + 45*x^19 + 44*x^18 + 107*x^17 + 46*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 54*x^12 + 23*x^11 + 124*x^10 + x^9 + 18*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 70*x^4 + 107*x^3 + 36*x^2 + 93*x + 114, x^95 + 15*x^93 + 50*x^92 + 85*x^91 + 36*x^90 + 83*x^89 + 70*x^88 + 85*x^87 + 104*x^86 + 107*x^85 + 82*x^84 + 105*x^83 + 124*x^82 + 15*x^81 + 54*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 110*x^76 + 83*x^75 + 44*x^74 + 101*x^73 + 122*x^72 + 75*x^71 + 72*x^70 + 21*x^69 + 126*x^68 + 23*x^67 + 116*x^66 + 17*x^65 + 26*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 82*x^59 + 40*x^58 + 62*x^57 + 124*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 52*x^52 + 122*x^51 + 24*x^50 + 54*x^49 + 28*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 70*x^43 + 24*x^42 + 42*x^41 + 116*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 60*x^36 + 110*x^35 + 40*x^34 + 98*x^33 + 116*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 122*x^28 + 9*x^27 + 116*x^26 + 63*x^25 + 94*x^24 + 105*x^23 + 72*x^22 + 87*x^21 + 90*x^20 + 77*x^19 + 44*x^18 + 11*x^17 + 78*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 86*x^12 + 55*x^11 + 124*x^10 + 33*x^9 + 114*x^8 + 111*x^7 + 104*x^6 + 113*x^5 + 102*x^4 + 75*x^3 + 36*x^2 + 61*x + 82, x^95 + 15*x^93 + 70*x^92 + 101*x^91 + 12*x^90 + 99*x^89 + 66*x^88 + 53*x^87 + 120*x^86 + 75*x^85 + 102*x^84 + 25*x^83 + 84*x^82 + 63*x^81 + 82*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 26*x^76 + 3*x^75 + 100*x^74 + 21*x^73 + 126*x^72 + 43*x^71 + 24*x^70 + 117*x^69 + 10*x^68 + 39*x^67 + 124*x^66 + 33*x^65 + 30*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 124*x^60 + 114*x^59 + 56*x^58 + 94*x^57 + 84*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 124*x^52 + 90*x^51 + 8*x^50 + 22*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 52*x^44 + 38*x^43 + 8*x^42 + 10*x^41 + 124*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 84*x^36 + 14*x^35 + 56*x^34 + 2*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 94*x^28 + 89*x^27 + 124*x^26 + 15*x^25 + 74*x^24 + 73*x^23 + 24*x^22 + 55*x^21 + 62*x^20 + 61*x^19 + 100*x^18 + 123*x^17 + 90*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 18*x^12 + 39*x^11 + 84*x^10 + 17*x^9 + 38*x^8 + 79*x^7 + 120*x^6 + 81*x^5 + 2*x^4 + 27*x^3 + 12*x^2 + 13*x + 6, x^95 + 15*x^93 + 94*x^92 + 101*x^91 + 12*x^90 + 3*x^89 + 90*x^88 + 53*x^87 + 56*x^86 + 11*x^85 + 94*x^84 + 25*x^83 + 20*x^82 + 31*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 3*x^75 + 100*x^74 + 117*x^73 + 38*x^72 + 43*x^71 + 88*x^70 + 53*x^69 + 18*x^68 + 39*x^67 + 60*x^66 + 65*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 56*x^58 + 30*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 8*x^50 + 86*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 8*x^42 + 74*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 56*x^34 + 66*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 89*x^27 + 124*x^26 + 47*x^25 + 66*x^24 + 73*x^23 + 88*x^22 + 119*x^21 + 22*x^20 + 61*x^19 + 36*x^18 + 91*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 39*x^11 + 84*x^10 + 113*x^9 + 46*x^8 + 79*x^7 + 56*x^6 + 17*x^5 + 106*x^4 + 27*x^3 + 76*x^2 + 45*x + 110, x^95 + 15*x^93 + 78*x^92 + 5*x^91 + 12*x^90 + 35*x^89 + 74*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 14*x^84 + 121*x^83 + 20*x^82 + 127*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 82*x^76 + 99*x^75 + 100*x^74 + 85*x^73 + 54*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 98*x^68 + 71*x^67 + 60*x^66 + 97*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 76*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 12*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 36*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 4*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 6*x^28 + 121*x^27 + 124*x^26 + 79*x^25 + 114*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 6*x^20 + 29*x^19 + 36*x^18 + 59*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 106*x^12 + 7*x^11 + 84*x^10 + 81*x^9 + 126*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 122*x^4 + 59*x^3 + 76*x^2 + 77*x + 126, x^95 + 15*x^93 + 122*x^92 + 5*x^91 + 84*x^90 + 3*x^89 + 94*x^88 + 117*x^87 + 72*x^86 + 11*x^85 + 26*x^84 + 121*x^83 + 76*x^82 + 31*x^81 + 14*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 38*x^76 + 99*x^75 + 60*x^74 + 117*x^73 + 98*x^72 + 107*x^71 + 40*x^70 + 53*x^69 + 118*x^68 + 71*x^67 + 100*x^66 + 65*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 4*x^60 + 50*x^59 + 8*x^58 + 30*x^57 + 108*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 4*x^52 + 26*x^51 + 56*x^50 + 86*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 76*x^44 + 102*x^43 + 56*x^42 + 74*x^41 + 68*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 44*x^36 + 78*x^35 + 8*x^34 + 66*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 98*x^28 + 121*x^27 + 100*x^26 + 47*x^25 + 86*x^24 + 9*x^23 + 40*x^22 + 119*x^21 + 66*x^20 + 29*x^19 + 60*x^18 + 91*x^17 + 6*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 46*x^12 + 7*x^11 + 76*x^10 + 113*x^9 + 58*x^8 + 15*x^7 + 72*x^6 + 17*x^5 + 126*x^4 + 59*x^3 + 84*x^2 + 45*x + 26, x^95 + 15*x^93 + 22*x^92 + 101*x^91 + 108*x^90 + 99*x^89 + 114*x^88 + 53*x^87 + 56*x^86 + 75*x^85 + 54*x^84 + 25*x^83 + 116*x^82 + 63*x^81 + 2*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 74*x^76 + 3*x^75 + 4*x^74 + 21*x^73 + 78*x^72 + 43*x^71 + 88*x^70 + 117*x^69 + 58*x^68 + 39*x^67 + 92*x^66 + 33*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 28*x^60 + 114*x^59 + 120*x^58 + 94*x^57 + 52*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 28*x^52 + 90*x^51 + 72*x^50 + 22*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 20*x^44 + 38*x^43 + 72*x^42 + 10*x^41 + 28*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 52*x^36 + 14*x^35 + 120*x^34 + 2*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 110*x^28 + 89*x^27 + 92*x^26 + 15*x^25 + 58*x^24 + 73*x^23 + 88*x^22 + 55*x^21 + 78*x^20 + 61*x^19 + 4*x^18 + 123*x^17 + 74*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 2*x^12 + 39*x^11 + 116*x^10 + 17*x^9 + 54*x^8 + 79*x^7 + 56*x^6 + 81*x^5 + 114*x^4 + 27*x^3 + 108*x^2 + 13*x + 22, x^95 + 15*x^93 + 38*x^92 + 21*x^91 + 28*x^90 + 115*x^89 + 18*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 102*x^84 + 41*x^83 + 4*x^82 + 111*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 122*x^76 + 19*x^75 + 20*x^74 + 69*x^73 + 110*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 74*x^68 + 87*x^67 + 12*x^66 + 49*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 62*x^28 + 73*x^27 + 76*x^26 + 95*x^25 + 90*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 62*x^20 + 13*x^19 + 84*x^18 + 107*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 114*x^12 + 119*x^11 + 68*x^10 + x^9 + 86*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 66*x^4 + 11*x^3 + 92*x^2 + 93*x + 86, x^95 + 15*x^93 + 30*x^92 + 5*x^91 + 12*x^90 + 35*x^89 + 90*x^88 + 117*x^87 + 56*x^86 + 75*x^85 + 30*x^84 + 121*x^83 + 20*x^82 + 127*x^81 + 74*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 2*x^76 + 99*x^75 + 100*x^74 + 85*x^73 + 38*x^72 + 107*x^71 + 88*x^70 + 117*x^69 + 82*x^68 + 71*x^67 + 60*x^66 + 97*x^65 + 38*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 50*x^59 + 56*x^58 + 94*x^57 + 68*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 26*x^51 + 8*x^50 + 22*x^49 + 100*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 102*x^43 + 8*x^42 + 10*x^41 + 76*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 78*x^35 + 56*x^34 + 2*x^33 + 12*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 22*x^28 + 121*x^27 + 124*x^26 + 79*x^25 + 66*x^24 + 9*x^23 + 88*x^22 + 55*x^21 + 86*x^20 + 29*x^19 + 36*x^18 + 59*x^17 + 50*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 90*x^12 + 7*x^11 + 84*x^10 + 81*x^9 + 46*x^8 + 15*x^7 + 56*x^6 + 81*x^5 + 42*x^4 + 59*x^3 + 76*x^2 + 77*x + 110, x^95 + 15*x^93 + 74*x^92 + 101*x^91 + 84*x^90 + 99*x^89 + 46*x^88 + 53*x^87 + 72*x^86 + 75*x^85 + 42*x^84 + 25*x^83 + 76*x^82 + 63*x^81 + 30*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 86*x^76 + 3*x^75 + 60*x^74 + 21*x^73 + 18*x^72 + 43*x^71 + 40*x^70 + 117*x^69 + 102*x^68 + 39*x^67 + 100*x^66 + 33*x^65 + 114*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 8*x^58 + 94*x^57 + 12*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 56*x^50 + 22*x^49 + 44*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 56*x^42 + 10*x^41 + 36*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 8*x^34 + 2*x^33 + 36*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 89*x^27 + 100*x^26 + 15*x^25 + 102*x^24 + 73*x^23 + 40*x^22 + 55*x^21 + 18*x^20 + 61*x^19 + 60*x^18 + 123*x^17 + 86*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 30*x^12 + 39*x^11 + 76*x^10 + 17*x^9 + 42*x^8 + 79*x^7 + 72*x^6 + 81*x^5 + 46*x^4 + 27*x^3 + 84*x^2 + 13*x + 74, x^95 + 15*x^93 + 10*x^92 + 101*x^91 + 116*x^90 + 35*x^89 + 14*x^88 + 53*x^87 + 8*x^86 + 75*x^85 + 42*x^84 + 25*x^83 + 44*x^82 + 127*x^81 + 62*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 22*x^76 + 3*x^75 + 28*x^74 + 85*x^73 + 50*x^72 + 43*x^71 + 104*x^70 + 117*x^69 + 102*x^68 + 39*x^67 + 4*x^66 + 97*x^65 + 82*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 114*x^59 + 72*x^58 + 94*x^57 + 76*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 36*x^52 + 90*x^51 + 120*x^50 + 22*x^49 + 108*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 38*x^43 + 120*x^42 + 10*x^41 + 100*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 12*x^36 + 14*x^35 + 72*x^34 + 2*x^33 + 100*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 89*x^27 + 4*x^26 + 79*x^25 + 70*x^24 + 73*x^23 + 104*x^22 + 55*x^21 + 18*x^20 + 61*x^19 + 28*x^18 + 59*x^17 + 118*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 94*x^12 + 39*x^11 + 44*x^10 + 81*x^9 + 74*x^8 + 79*x^7 + 8*x^6 + 81*x^5 + 46*x^4 + 27*x^3 + 116*x^2 + 77*x + 42, x^95 + 15*x^93 + 2*x^92 + 117*x^91 + 100*x^90 + 115*x^89 + 86*x^88 + 21*x^87 + 104*x^86 + 43*x^85 + 98*x^84 + 73*x^83 + 60*x^82 + 111*x^81 + 6*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 30*x^76 + 51*x^75 + 108*x^74 + 69*x^73 + 106*x^72 + 11*x^71 + 72*x^70 + 85*x^69 + 110*x^68 + 55*x^67 + 52*x^66 + 49*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 84*x^60 + 18*x^59 + 40*x^58 + 126*x^57 + 28*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 84*x^52 + 58*x^51 + 24*x^50 + 118*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 60*x^44 + 6*x^43 + 24*x^42 + 106*x^41 + 84*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 28*x^36 + 46*x^35 + 40*x^34 + 34*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 10*x^28 + 41*x^27 + 52*x^26 + 95*x^25 + 46*x^24 + 41*x^23 + 72*x^22 + 23*x^21 + 42*x^20 + 45*x^19 + 108*x^18 + 107*x^17 + 94*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 70*x^12 + 23*x^11 + 60*x^10 + x^9 + 34*x^8 + 47*x^7 + 104*x^6 + 49*x^5 + 22*x^4 + 107*x^3 + 100*x^2 + 93*x + 66, x^95 + 15*x^93 + 10*x^92 + 117*x^91 + 4*x^90 + 19*x^89 + 62*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 74*x^84 + 73*x^83 + 92*x^82 + 79*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 86*x^76 + 51*x^75 + 76*x^74 + 37*x^73 + 66*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 6*x^68 + 55*x^67 + 20*x^66 + 81*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 50*x^28 + 41*x^27 + 84*x^26 + 127*x^25 + 54*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 50*x^20 + 45*x^19 + 12*x^18 + 75*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 30*x^12 + 23*x^11 + 28*x^10 + 97*x^9 + 26*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 78*x^4 + 107*x^3 + 68*x^2 + 125*x + 26, x^95 + 15*x^93 + 54*x^92 + 21*x^91 + 92*x^90 + 115*x^89 + 34*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 54*x^84 + 41*x^83 + 68*x^82 + 111*x^81 + 82*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 106*x^76 + 19*x^75 + 84*x^74 + 69*x^73 + 94*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 122*x^68 + 87*x^67 + 76*x^66 + 49*x^65 + 94*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 92*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 20*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 28*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 52*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 84*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 60*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 52*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 124*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 14*x^28 + 73*x^27 + 12*x^26 + 95*x^25 + 42*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 78*x^20 + 13*x^19 + 20*x^18 + 107*x^17 + 90*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 34*x^12 + 119*x^11 + 4*x^10 + x^9 + 6*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 50*x^4 + 11*x^3 + 28*x^2 + 93*x + 70, x^95 + 15*x^93 + 74*x^92 + 53*x^91 + 4*x^90 + 83*x^89 + 126*x^88 + 21*x^87 + 104*x^86 + 107*x^85 + 10*x^84 + 9*x^83 + 92*x^82 + 15*x^81 + 14*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 115*x^75 + 76*x^74 + 101*x^73 + 2*x^72 + 11*x^71 + 72*x^70 + 21*x^69 + 70*x^68 + 119*x^67 + 20*x^66 + 17*x^65 + 66*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 18*x^59 + 104*x^58 + 62*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 58*x^51 + 88*x^50 + 54*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 6*x^43 + 88*x^42 + 42*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 46*x^35 + 104*x^34 + 98*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 105*x^27 + 84*x^26 + 63*x^25 + 118*x^24 + 41*x^23 + 72*x^22 + 87*x^21 + 114*x^20 + 109*x^19 + 12*x^18 + 11*x^17 + 6*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 87*x^11 + 28*x^10 + 33*x^9 + 90*x^8 + 47*x^7 + 104*x^6 + 113*x^5 + 14*x^4 + 43*x^3 + 68*x^2 + 61*x + 90, x^95 + 15*x^93 + 102*x^92 + 21*x^91 + 28*x^90 + 115*x^89 + 82*x^88 + 85*x^87 + 88*x^86 + 43*x^85 + 38*x^84 + 41*x^83 + 4*x^82 + 111*x^81 + 66*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 19*x^75 + 20*x^74 + 69*x^73 + 46*x^72 + 75*x^71 + 120*x^70 + 85*x^69 + 10*x^68 + 87*x^67 + 12*x^66 + 49*x^65 + 110*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 82*x^59 + 88*x^58 + 126*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 122*x^51 + 104*x^50 + 118*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 70*x^43 + 104*x^42 + 106*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 110*x^35 + 88*x^34 + 34*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 73*x^27 + 76*x^26 + 95*x^25 + 26*x^24 + 105*x^23 + 120*x^22 + 23*x^21 + 126*x^20 + 13*x^19 + 84*x^18 + 107*x^17 + 10*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 119*x^11 + 68*x^10 + x^9 + 22*x^8 + 111*x^7 + 88*x^6 + 49*x^5 + 2*x^4 + 11*x^3 + 92*x^2 + 93*x + 22, x^95 + 15*x^93 + 110*x^92 + 5*x^91 + 108*x^90 + 35*x^89 + 10*x^88 + 117*x^87 + 120*x^86 + 75*x^85 + 110*x^84 + 121*x^83 + 52*x^82 + 127*x^81 + 122*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 50*x^76 + 99*x^75 + 4*x^74 + 85*x^73 + 118*x^72 + 107*x^71 + 24*x^70 + 117*x^69 + 2*x^68 + 71*x^67 + 28*x^66 + 97*x^65 + 118*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 50*x^59 + 120*x^58 + 94*x^57 + 36*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 76*x^52 + 26*x^51 + 72*x^50 + 22*x^49 + 68*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 102*x^43 + 72*x^42 + 10*x^41 + 108*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 68*x^36 + 78*x^35 + 120*x^34 + 2*x^33 + 44*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 38*x^28 + 121*x^27 + 92*x^26 + 79*x^25 + 50*x^24 + 9*x^23 + 24*x^22 + 55*x^21 + 102*x^20 + 29*x^19 + 68*x^18 + 59*x^17 + 34*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 74*x^12 + 7*x^11 + 116*x^10 + 81*x^9 + 62*x^8 + 15*x^7 + 120*x^6 + 81*x^5 + 26*x^4 + 59*x^3 + 44*x^2 + 77*x + 126, x^95 + 15*x^93 + 94*x^92 + 37*x^91 + 44*x^90 + 3*x^89 + 122*x^88 + 53*x^87 + 120*x^86 + 11*x^85 + 30*x^84 + 89*x^83 + 116*x^82 + 31*x^81 + 42*x^80 + 103*x^79 + 80*x^78 + 41*x^77 + 66*x^76 + 67*x^75 + 68*x^74 + 117*x^73 + 6*x^72 + 43*x^71 + 24*x^70 + 53*x^69 + 82*x^68 + 103*x^67 + 92*x^66 + 65*x^65 + 70*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 108*x^60 + 114*x^59 + 120*x^58 + 30*x^57 + 4*x^56 + 114*x^55 + 112*x^54 + 14*x^53 + 44*x^52 + 90*x^51 + 72*x^50 + 86*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 4*x^44 + 38*x^43 + 72*x^42 + 74*x^41 + 12*x^40 + 22*x^39 + 112*x^38 + 42*x^37 + 100*x^36 + 14*x^35 + 120*x^34 + 66*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 86*x^28 + 25*x^27 + 28*x^26 + 47*x^25 + 98*x^24 + 73*x^23 + 24*x^22 + 119*x^21 + 86*x^20 + 125*x^19 + 4*x^18 + 91*x^17 + 18*x^16 + 59*x^15 + 80*x^14 + 21*x^13 + 26*x^12 + 103*x^11 + 52*x^10 + 113*x^9 + 14*x^8 + 79*x^7 + 120*x^6 + 17*x^5 + 42*x^4 + 91*x^3 + 108*x^2 + 45*x + 14, x^95 + 15*x^93 + 46*x^92 + 53*x^91 + 28*x^90 + 51*x^89 + 26*x^88 + 21*x^87 + 24*x^86 + 43*x^85 + 14*x^84 + 9*x^83 + 68*x^82 + 47*x^81 + 42*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 50*x^76 + 115*x^75 + 20*x^74 + 5*x^73 + 38*x^72 + 11*x^71 + 56*x^70 + 85*x^69 + 34*x^68 + 119*x^67 + 76*x^66 + 113*x^65 + 6*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 12*x^60 + 18*x^59 + 88*x^58 + 126*x^57 + 68*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 12*x^52 + 58*x^51 + 104*x^50 + 118*x^49 + 36*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 100*x^44 + 6*x^43 + 104*x^42 + 106*x^41 + 76*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 4*x^36 + 46*x^35 + 88*x^34 + 34*x^33 + 76*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 102*x^28 + 105*x^27 + 76*x^26 + 31*x^25 + 2*x^24 + 41*x^23 + 56*x^22 + 23*x^21 + 6*x^20 + 109*x^19 + 20*x^18 + 43*x^17 + 18*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 74*x^12 + 87*x^11 + 68*x^10 + 65*x^9 + 46*x^8 + 47*x^7 + 24*x^6 + 49*x^5 + 58*x^4 + 43*x^3 + 28*x^2 + 29*x + 78, x^95 + 15*x^93 + 74*x^92 + 85*x^91 + 68*x^90 + 51*x^89 + 62*x^88 + 85*x^87 + 104*x^86 + 43*x^85 + 10*x^84 + 105*x^83 + 28*x^82 + 47*x^81 + 78*x^80 + 39*x^79 + 112*x^78 + 105*x^77 + 22*x^76 + 83*x^75 + 12*x^74 + 5*x^73 + 66*x^72 + 75*x^71 + 72*x^70 + 85*x^69 + 70*x^68 + 23*x^67 + 84*x^66 + 113*x^65 + 2*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 36*x^60 + 82*x^59 + 104*x^58 + 126*x^57 + 44*x^56 + 50*x^55 + 80*x^54 + 78*x^53 + 100*x^52 + 122*x^51 + 88*x^50 + 118*x^49 + 12*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 44*x^44 + 70*x^43 + 88*x^42 + 106*x^41 + 4*x^40 + 86*x^39 + 80*x^38 + 106*x^37 + 76*x^36 + 110*x^35 + 104*x^34 + 34*x^33 + 68*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 114*x^28 + 9*x^27 + 20*x^26 + 31*x^25 + 54*x^24 + 105*x^23 + 72*x^22 + 23*x^21 + 114*x^20 + 77*x^19 + 76*x^18 + 43*x^17 + 70*x^16 + 123*x^15 + 112*x^14 + 85*x^13 + 94*x^12 + 55*x^11 + 92*x^10 + 65*x^9 + 26*x^8 + 111*x^7 + 104*x^6 + 49*x^5 + 14*x^4 + 75*x^3 + 4*x^2 + 29*x + 26, x^95 + 15*x^93 + 114*x^92 + 5*x^91 + 116*x^90 + 35*x^89 + 118*x^88 + 117*x^87 + 72*x^86 + 75*x^85 + 50*x^84 + 121*x^83 + 108*x^82 + 127*x^81 + 70*x^80 + 103*x^79 + 48*x^78 + 41*x^77 + 110*x^76 + 99*x^75 + 28*x^74 + 85*x^73 + 10*x^72 + 107*x^71 + 40*x^70 + 117*x^69 + 94*x^68 + 71*x^67 + 68*x^66 + 97*x^65 + 74*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 52*x^60 + 50*x^59 + 72*x^58 + 94*x^57 + 92*x^56 + 114*x^55 + 16*x^54 + 14*x^53 + 116*x^52 + 26*x^51 + 120*x^50 + 22*x^49 + 60*x^48 + 110*x^47 + 32*x^46 + 50*x^45 + 92*x^44 + 102*x^43 + 120*x^42 + 10*x^41 + 20*x^40 + 22*x^39 + 16*x^38 + 42*x^37 + 124*x^36 + 78*x^35 + 72*x^34 + 2*x^33 + 84*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 58*x^28 + 121*x^27 + 4*x^26 + 79*x^25 + 78*x^24 + 9*x^23 + 40*x^22 + 55*x^21 + 58*x^20 + 29*x^19 + 92*x^18 + 59*x^17 + 30*x^16 + 59*x^15 + 48*x^14 + 21*x^13 + 86*x^12 + 7*x^11 + 44*x^10 + 81*x^9 + 66*x^8 + 15*x^7 + 72*x^6 + 81*x^5 + 70*x^4 + 59*x^3 + 52*x^2 + 77*x + 66, x^95 + 15*x^93 + 102*x^92 + 53*x^91 + 92*x^90 + 83*x^89 + 18*x^88 + 21*x^87 + 88*x^86 + 107*x^85 + 38*x^84 + 9*x^83 + 68*x^82 + 15*x^81 + 2*x^80 + 39*x^79 + 16*x^78 + 105*x^77 + 58*x^76 + 115*x^75 + 84*x^74 + 101*x^73 + 110*x^72 + 11*x^71 + 120*x^70 + 21*x^69 + 10*x^68 + 119*x^67 + 76*x^66 + 17*x^65 + 46*x^64 + 10*x^63 + 64*x^62 + 22*x^61 + 60*x^60 + 18*x^59 + 88*x^58 + 62*x^57 + 116*x^56 + 50*x^55 + 48*x^54 + 78*x^53 + 124*x^52 + 58*x^51 + 104*x^50 + 54*x^49 + 20*x^48 + 110*x^47 + 96*x^46 + 50*x^45 + 116*x^44 + 6*x^43 + 104*x^42 + 42*x^41 + 92*x^40 + 86*x^39 + 48*x^38 + 106*x^37 + 84*x^36 + 46*x^35 + 88*x^34 + 98*x^33 + 28*x^32 + 101*x^31 + 64*x^30 + 107*x^29 + 126*x^28 + 105*x^27 + 12*x^26 + 63*x^25 + 90*x^24 + 41*x^23 + 120*x^22 + 87*x^21 + 126*x^20 + 109*x^19 + 20*x^18 + 11*x^17 + 74*x^16 + 123*x^15 + 16*x^14 + 85*x^13 + 50*x^12 + 87*x^11 + 4*x^10 + 33*x^9 + 86*x^8 + 47*x^7 + 88*x^6 + 113*x^5 + 2*x^4 + 43*x^3 + 28*x^2 + 61*x + 86}


In [9]:
#precompute Seidel char polys classes n=93, e=7
#scc937=SeidelCharPolysMod(93,7)

In [10]:
scc937={x^93 + 74*x^91 + 76*x^90 + 43*x^89 + 92*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 68*x^82 + 99*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 117*x^73 + 116*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 108*x^66 + 69*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 87*x^25 + 12*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 20*x^18 + 15*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 17*x^9 + 36*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 60*x^2 + x + 108, x^93 + 74*x^91 + 20*x^90 + 75*x^89 + 100*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 92*x^82 + 67*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 85*x^73 + 76*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 116*x^66 + 101*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 119*x^25 + 52*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 12*x^18 + 111*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 113*x^9 + 28*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 36*x^2 + 33*x + 84, x^93 + 74*x^91 + 56*x^90 + 51*x^89 + 8*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 40*x^82 + 91*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 13*x^73 + 88*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 56*x^66 + 45*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 127*x^25 + 40*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 72*x^18 + 103*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 73*x^9 + 120*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 88*x^2 + 73*x + 40, x^93 + 74*x^91 + 124*x^90 + 59*x^89 + 124*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 84*x^82 + 83*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 37*x^73 + 84*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 28*x^66 + 21*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 39*x^25 + 44*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 100*x^18 + 63*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + x^9 + 4*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 44*x^2 + 17*x + 12, x^93 + 74*x^91 + 4*x^90 + 59*x^89 + 68*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 44*x^82 + 83*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 37*x^73 + 108*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 100*x^66 + 21*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 39*x^25 + 20*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 28*x^18 + 63*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + x^9 + 60*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 84*x^2 + 17*x + 52, x^93 + 74*x^91 + 60*x^90 + 75*x^89 + 44*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 20*x^82 + 67*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 85*x^73 + 100*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 92*x^66 + 101*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 119*x^25 + 28*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 36*x^18 + 111*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 113*x^9 + 84*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 108*x^2 + 33*x + 124, x^93 + 74*x^91 + 8*x^90 + 35*x^89 + 8*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 24*x^82 + 107*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 93*x^73 + 88*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 8*x^66 + 93*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 47*x^25 + 40*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 120*x^18 + 55*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 89*x^9 + 120*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 104*x^2 + 57*x + 40, x^93 + 74*x^91 + 64*x^90 + 115*x^89 + 112*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 38*x^83 + 91*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 77*x^73 + 80*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 50*x^67 + 45*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 63*x^25 + 48*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 94*x^19 + 103*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 9*x^9 + 16*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 42*x^3 + 73*x + 112, x^93 + 74*x^91 + 92*x^90 + 75*x^89 + 12*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 52*x^82 + 3*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 85*x^73 + 4*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 60*x^66 + 37*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 119*x^25 + 124*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 68*x^18 + 47*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 113*x^9 + 116*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 76*x^2 + 97*x + 28, x^93 + 74*x^91 + 52*x^90 + 27*x^89 + 84*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 60*x^82 + 115*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 69*x^73 + 28*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 20*x^66 + 117*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 7*x^25 + 100*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 108*x^18 + 95*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 33*x^9 + 44*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 68*x^2 + 113*x + 4, x^93 + 74*x^91 + 72*x^90 + 35*x^89 + 8*x^88 + 68*x^87 + 48*x^86 + x^85 + 112*x^84 + 102*x^83 + 24*x^82 + 43*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 93*x^73 + 88*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 8*x^66 + 29*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 47*x^25 + 40*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 120*x^18 + 119*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 89*x^9 + 120*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 104*x^2 + 121*x + 104, x^93 + 74*x^91 + 76*x^90 + 107*x^89 + 124*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 68*x^82 + 35*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 53*x^73 + 84*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 108*x^66 + 5*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 23*x^25 + 44*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 20*x^18 + 79*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 81*x^9 + 4*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 60*x^2 + 65*x + 12, x^93 + 74*x^91 + 16*x^90 + 35*x^89 + 80*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 48*x^82 + 107*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 93*x^73 + 112*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 16*x^66 + 93*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 47*x^25 + 16*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 112*x^18 + 55*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 89*x^9 + 48*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 80*x^2 + 57*x + 16, x^93 + 74*x^91 + 112*x^90 + 19*x^89 + 96*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 80*x^82 + 123*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 45*x^73 + 32*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 112*x^66 + 13*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 95*x^25 + 96*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 16*x^18 + 7*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 105*x^9 + 32*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 48*x^2 + 41*x + 96, x^93 + 74*x^91 + 8*x^90 + 3*x^89 + 40*x^88 + 4*x^87 + 112*x^86 + x^85 + 112*x^84 + 38*x^83 + 24*x^82 + 11*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 125*x^73 + 56*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 8*x^66 + 61*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 15*x^25 + 72*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 120*x^18 + 87*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 121*x^9 + 88*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 104*x^2 + 25*x + 72, x^93 + 74*x^91 + 4*x^90 + 123*x^89 + 36*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 108*x^82 + 83*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 101*x^73 + 12*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 36*x^66 + 21*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 103*x^25 + 116*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 92*x^18 + 63*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 65*x^9 + 92*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 20*x^2 + 17*x + 84, x^93 + 74*x^91 + 20*x^90 + 59*x^89 + 20*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 92*x^82 + 83*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 37*x^73 + 92*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 116*x^66 + 21*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 39*x^25 + 36*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 12*x^18 + 63*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + x^9 + 108*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 36*x^2 + 17*x + 68, x^93 + 74*x^91 + 92*x^90 + 107*x^89 + 76*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 52*x^82 + 99*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 53*x^73 + 68*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 60*x^66 + 69*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 23*x^25 + 60*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 68*x^18 + 15*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 81*x^9 + 52*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 76*x^2 + x + 92, x^93 + 74*x^91 + 8*x^90 + 3*x^89 + 72*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 88*x^82 + 75*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 125*x^73 + 24*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 72*x^66 + 125*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 15*x^25 + 104*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 56*x^18 + 23*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 121*x^9 + 56*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 40*x^2 + 89*x + 40, x^93 + 74*x^91 + 44*x^90 + 123*x^89 + 108*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 36*x^82 + 83*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 101*x^73 + 36*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 12*x^66 + 21*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 103*x^25 + 92*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 116*x^18 + 63*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 65*x^9 + 20*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 92*x^2 + 17*x + 124, x^93 + 74*x^91 + 40*x^90 + 51*x^89 + 88*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 56*x^82 + 27*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 13*x^73 + 72*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 104*x^66 + 109*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 127*x^25 + 56*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 24*x^18 + 39*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 73*x^9 + 40*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 72*x^2 + 9*x + 120, x^93 + 74*x^91 + 52*x^90 + 27*x^89 + 52*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 124*x^82 + 51*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 69*x^73 + 60*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 84*x^66 + 53*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 7*x^25 + 68*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 44*x^18 + 31*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 33*x^9 + 76*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 4*x^2 + 49*x + 36, x^93 + 74*x^91 + 4*x^90 + 91*x^89 + 4*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 108*x^82 + 115*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 5*x^73 + 44*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 36*x^66 + 117*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 71*x^25 + 84*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 92*x^18 + 95*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 97*x^9 + 124*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 20*x^2 + 113*x + 52, x^93 + 74*x^91 + 112*x^90 + 51*x^89 + 32*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 80*x^82 + 91*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 13*x^73 + 96*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 112*x^66 + 45*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 127*x^25 + 32*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 16*x^18 + 103*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 73*x^9 + 96*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 48*x^2 + 73*x + 32, x^93 + 74*x^91 + 32*x^90 + 51*x^89 + 16*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 102*x^83 + 96*x^82 + 91*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 13*x^73 + 48*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 114*x^67 + 32*x^66 + 45*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 127*x^25 + 80*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 30*x^19 + 96*x^18 + 103*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 73*x^9 + 112*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 106*x^3 + 32*x^2 + 73*x + 80, x^93 + 74*x^91 + 28*x^90 + 123*x^89 + 60*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 52*x^82 + 19*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 101*x^73 + 20*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 60*x^66 + 85*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 103*x^25 + 108*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 68*x^18 + 127*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 65*x^9 + 68*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 76*x^2 + 81*x + 76, x^93 + 74*x^91 + 20*x^90 + 43*x^89 + 36*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 28*x^82 + 35*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 117*x^73 + 12*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 52*x^66 + 5*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 87*x^25 + 116*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 76*x^18 + 79*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 17*x^9 + 92*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 100*x^2 + 65*x + 84, x^93 + 74*x^91 + 92*x^90 + 59*x^89 + 28*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 52*x^82 + 19*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 37*x^73 + 52*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 60*x^66 + 85*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 39*x^25 + 76*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 68*x^18 + 127*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + x^9 + 100*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 76*x^2 + 81*x + 108, x^93 + 74*x^91 + 48*x^90 + 3*x^89 + 48*x^88 + 4*x^87 + 32*x^86 + x^85 + 32*x^84 + 38*x^83 + 16*x^82 + 11*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 125*x^73 + 16*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 48*x^66 + 61*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 15*x^25 + 112*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 80*x^18 + 87*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 121*x^9 + 80*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 112*x^2 + 25*x + 112, x^93 + 74*x^91 + 124*x^90 + 107*x^89 + 108*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 20*x^82 + 99*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 53*x^73 + 36*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 92*x^66 + 69*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 23*x^25 + 92*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 36*x^18 + 15*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 81*x^9 + 20*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 108*x^2 + x + 124, x^93 + 74*x^91 + 40*x^90 + 19*x^89 + 88*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 120*x^82 + 123*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 45*x^73 + 72*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 40*x^66 + 13*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 95*x^25 + 56*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 88*x^18 + 7*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 105*x^9 + 40*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 8*x^2 + 41*x + 56, x^93 + 74*x^91 + 16*x^90 + 115*x^89 + 64*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 102*x^83 + 48*x^82 + 27*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 77*x^73 + 64*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 114*x^67 + 16*x^66 + 109*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 63*x^25 + 64*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 30*x^19 + 112*x^18 + 39*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 9*x^9 + 64*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 106*x^3 + 80*x^2 + 9*x + 64, x^93 + 74*x^91 + 88*x^90 + 51*x^89 + 8*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 8*x^82 + 91*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 13*x^73 + 88*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 88*x^66 + 45*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 127*x^25 + 40*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 40*x^18 + 103*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 73*x^9 + 120*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 120*x^2 + 73*x + 40, x^93 + 74*x^91 + 64*x^90 + 115*x^89 + 48*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 38*x^83 + 91*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 77*x^73 + 16*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 50*x^67 + 45*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 63*x^25 + 112*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 94*x^19 + 103*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 9*x^9 + 80*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 42*x^3 + 73*x + 48, x^93 + 74*x^91 + 68*x^90 + 107*x^89 + 20*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 44*x^82 + 99*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 53*x^73 + 92*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 100*x^66 + 69*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 23*x^25 + 36*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 28*x^18 + 15*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 81*x^9 + 108*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 84*x^2 + x + 4, x^93 + 74*x^91 + 16*x^90 + 99*x^89 + 112*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 48*x^82 + 43*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 29*x^73 + 80*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 16*x^66 + 29*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 111*x^25 + 48*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 112*x^18 + 119*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 25*x^9 + 16*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 80*x^2 + 121*x + 48, x^93 + 74*x^91 + 24*x^90 + 3*x^89 + 24*x^88 + 4*x^87 + 80*x^86 + x^85 + 16*x^84 + 38*x^83 + 72*x^82 + 11*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 125*x^73 + 8*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 24*x^66 + 61*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 15*x^25 + 120*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 104*x^18 + 87*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 121*x^9 + 104*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 56*x^2 + 25*x + 120, x^93 + 74*x^91 + 28*x^90 + 91*x^89 + 28*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 52*x^82 + 51*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 5*x^73 + 52*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 60*x^66 + 53*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 71*x^25 + 76*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 68*x^18 + 31*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 97*x^9 + 100*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 76*x^2 + 49*x + 44, x^93 + 74*x^91 + 16*x^90 + 99*x^89 + 48*x^88 + 68*x^87 + 32*x^86 + x^85 + 96*x^84 + 102*x^83 + 112*x^82 + 107*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 29*x^73 + 16*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 80*x^66 + 93*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 111*x^25 + 112*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 48*x^18 + 55*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 25*x^9 + 80*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 16*x^2 + 57*x + 48, x^93 + 74*x^91 + 104*x^90 + 115*x^89 + 120*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 56*x^82 + 27*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 77*x^73 + 40*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 104*x^66 + 109*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 63*x^25 + 88*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 24*x^18 + 39*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 9*x^9 + 8*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 72*x^2 + 9*x + 88, x^93 + 74*x^91 + 120*x^90 + 51*x^89 + 104*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 104*x^82 + 91*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 13*x^73 + 120*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 120*x^66 + 45*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 127*x^25 + 8*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 8*x^18 + 103*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 73*x^9 + 24*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 24*x^2 + 73*x + 8, x^93 + 74*x^91 + 52*x^90 + 43*x^89 + 4*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 60*x^82 + 99*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 117*x^73 + 44*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 20*x^66 + 69*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 87*x^25 + 84*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 108*x^18 + 15*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 17*x^9 + 124*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 68*x^2 + x + 116, x^93 + 74*x^91 + 28*x^90 + 107*x^89 + 76*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 116*x^82 + 99*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 53*x^73 + 68*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 124*x^66 + 69*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 23*x^25 + 60*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 4*x^18 + 15*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 81*x^9 + 52*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 12*x^2 + x + 92, x^93 + 74*x^91 + 8*x^90 + 99*x^89 + 72*x^88 + 68*x^87 + 48*x^86 + x^85 + 112*x^84 + 102*x^83 + 88*x^82 + 107*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 29*x^73 + 24*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 72*x^66 + 93*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 111*x^25 + 104*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 56*x^18 + 55*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 25*x^9 + 56*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 40*x^2 + 57*x + 40, x^93 + 74*x^91 + 12*x^90 + 59*x^89 + 76*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 4*x^82 + 83*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 37*x^73 + 68*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 44*x^66 + 21*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 39*x^25 + 60*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 84*x^18 + 63*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + x^9 + 52*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 124*x^2 + 17*x + 28, x^93 + 74*x^91 + 48*x^90 + 51*x^89 + 64*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 80*x^82 + 27*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 13*x^73 + 64*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 112*x^66 + 109*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 127*x^25 + 64*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 16*x^18 + 39*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 73*x^9 + 64*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 48*x^2 + 9*x, x^93 + 74*x^91 + 96*x^90 + 99*x^89 + 32*x^88 + 68*x^87 + x^85 + 102*x^83 + 96*x^82 + 107*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 29*x^73 + 96*x^72 + 116*x^71 + 7*x^69 + 114*x^67 + 32*x^66 + 93*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 111*x^25 + 32*x^24 + 116*x^23 + 37*x^21 + 30*x^19 + 96*x^18 + 55*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 25*x^9 + 96*x^8 + 68*x^7 + 27*x^5 + 106*x^3 + 32*x^2 + 57*x + 96, x^93 + 74*x^91 + 108*x^90 + 27*x^89 + 108*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 100*x^82 + 51*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 69*x^73 + 36*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 76*x^66 + 53*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 7*x^25 + 92*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 52*x^18 + 31*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 33*x^9 + 20*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 28*x^2 + 49*x + 124, x^93 + 74*x^91 + 32*x^90 + 83*x^89 + 16*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 102*x^83 + 96*x^82 + 59*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 109*x^73 + 48*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 114*x^67 + 32*x^66 + 77*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 31*x^25 + 80*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 30*x^19 + 96*x^18 + 71*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 41*x^9 + 112*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 106*x^3 + 32*x^2 + 105*x + 80, x^93 + 74*x^91 + 88*x^90 + 35*x^89 + 24*x^88 + 68*x^87 + 16*x^86 + x^85 + 80*x^84 + 102*x^83 + 72*x^82 + 43*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 93*x^73 + 8*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 24*x^66 + 29*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 47*x^25 + 120*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 104*x^18 + 119*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 89*x^9 + 104*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 56*x^2 + 121*x + 56, x^93 + 74*x^91 + 80*x^90 + 51*x^89 + 96*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 112*x^82 + 91*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 13*x^73 + 32*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 80*x^66 + 45*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 127*x^25 + 96*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 48*x^18 + 103*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 73*x^9 + 32*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 16*x^2 + 73*x + 96, x^93 + 74*x^91 + 20*x^90 + 91*x^89 + 116*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 92*x^82 + 51*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 5*x^73 + 124*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 116*x^66 + 53*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 71*x^25 + 4*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 12*x^18 + 31*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 97*x^9 + 12*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 36*x^2 + 49*x + 36, x^93 + 74*x^91 + 76*x^90 + 43*x^89 + 124*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 68*x^82 + 99*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 117*x^73 + 84*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 108*x^66 + 69*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 87*x^25 + 44*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 20*x^18 + 15*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 17*x^9 + 4*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 60*x^2 + x + 12, x^93 + 74*x^91 + 116*x^90 + 91*x^89 + 52*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 124*x^82 + 51*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 5*x^73 + 60*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 84*x^66 + 53*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 71*x^25 + 68*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 44*x^18 + 31*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 97*x^9 + 76*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 4*x^2 + 49*x + 100, x^93 + 74*x^91 + 4*x^90 + 59*x^89 + 36*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 44*x^82 + 83*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 37*x^73 + 12*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 100*x^66 + 21*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 39*x^25 + 116*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 28*x^18 + 63*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + x^9 + 92*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 84*x^2 + 17*x + 20, x^93 + 74*x^91 + 60*x^90 + 91*x^89 + 124*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 20*x^82 + 51*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 5*x^73 + 84*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 92*x^66 + 53*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 71*x^25 + 44*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 36*x^18 + 31*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 97*x^9 + 4*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 108*x^2 + 49*x + 12, x^93 + 74*x^91 + 84*x^90 + 43*x^89 + 36*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 28*x^82 + 99*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 117*x^73 + 12*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 52*x^66 + 69*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 87*x^25 + 116*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 76*x^18 + 15*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 17*x^9 + 92*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 100*x^2 + x + 20, x^93 + 74*x^91 + 32*x^90 + 19*x^89 + 112*x^88 + 4*x^87 + 97*x^85 + 96*x^84 + 38*x^83 + 32*x^82 + 59*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 45*x^73 + 80*x^72 + 52*x^71 + 103*x^69 + 96*x^68 + 50*x^67 + 96*x^66 + 77*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 95*x^25 + 48*x^24 + 52*x^23 + 5*x^21 + 96*x^20 + 94*x^19 + 32*x^18 + 71*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 105*x^9 + 16*x^8 + 4*x^7 + 123*x^5 + 96*x^4 + 42*x^3 + 96*x^2 + 105*x + 112, x^93 + 74*x^91 + 56*x^90 + 115*x^89 + 40*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 40*x^82 + 27*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 77*x^73 + 56*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 56*x^66 + 109*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 63*x^25 + 72*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 72*x^18 + 39*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 9*x^9 + 88*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 88*x^2 + 9*x + 72, x^93 + 74*x^91 + 56*x^90 + 51*x^89 + 8*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 104*x^82 + 27*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 13*x^73 + 88*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 120*x^66 + 109*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 127*x^25 + 40*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 8*x^18 + 39*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 73*x^9 + 120*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 24*x^2 + 9*x + 104, x^93 + 74*x^91 + 28*x^90 + 91*x^89 + 124*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 52*x^82 + 51*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 5*x^73 + 84*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 60*x^66 + 53*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 71*x^25 + 44*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 68*x^18 + 31*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 97*x^9 + 4*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 76*x^2 + 49*x + 12, x^93 + 74*x^91 + 112*x^90 + 3*x^89 + 112*x^88 + 4*x^87 + 32*x^86 + x^85 + 32*x^84 + 38*x^83 + 80*x^82 + 11*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 125*x^73 + 80*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 112*x^66 + 61*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 15*x^25 + 48*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 16*x^18 + 87*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 121*x^9 + 16*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 48*x^2 + 25*x + 48, x^93 + 74*x^91 + 124*x^90 + 11*x^89 + 108*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 84*x^82 + 3*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 21*x^73 + 36*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 28*x^66 + 37*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 55*x^25 + 92*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 100*x^18 + 47*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 49*x^9 + 20*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 44*x^2 + 97*x + 60, x^93 + 74*x^91 + 64*x^90 + 19*x^89 + 48*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 38*x^83 + 59*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 45*x^73 + 16*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 50*x^67 + 77*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 95*x^25 + 112*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 94*x^19 + 71*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 105*x^9 + 80*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 42*x^3 + 105*x + 48, x^93 + 74*x^91 + 56*x^90 + 35*x^89 + 120*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 40*x^82 + 107*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 93*x^73 + 40*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 56*x^66 + 93*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 47*x^25 + 88*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 72*x^18 + 55*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 89*x^9 + 8*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 88*x^2 + 57*x + 88, x^93 + 74*x^91 + 72*x^90 + 115*x^89 + 120*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 24*x^82 + 91*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 77*x^73 + 40*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 8*x^66 + 45*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 63*x^25 + 88*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 120*x^18 + 103*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 9*x^9 + 8*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 104*x^2 + 73*x + 24, x^93 + 74*x^91 + 124*x^90 + 123*x^89 + 92*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 20*x^82 + 83*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 101*x^73 + 116*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 92*x^66 + 21*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 103*x^25 + 12*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 36*x^18 + 63*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 65*x^9 + 36*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 108*x^2 + 17*x + 44, x^93 + 74*x^91 + 16*x^90 + 99*x^89 + 16*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 48*x^82 + 43*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 29*x^73 + 48*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 16*x^66 + 29*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 111*x^25 + 80*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 112*x^18 + 119*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 25*x^9 + 112*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 80*x^2 + 121*x + 80, x^93 + 74*x^91 + 116*x^90 + 43*x^89 + 4*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 60*x^82 + 35*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 117*x^73 + 44*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 20*x^66 + 5*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 87*x^25 + 84*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 108*x^18 + 79*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 17*x^9 + 124*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 68*x^2 + 65*x + 52, x^93 + 74*x^91 + 83*x^89 + 80*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 38*x^83 + 64*x^82 + 123*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 109*x^73 + 112*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 50*x^67 + 64*x^66 + 13*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 31*x^25 + 16*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 94*x^19 + 64*x^18 + 7*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 41*x^9 + 48*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 42*x^3 + 64*x^2 + 41*x + 80, x^93 + 74*x^91 + 28*x^90 + 107*x^89 + 76*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 52*x^82 + 35*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 53*x^73 + 68*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 60*x^66 + 5*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 23*x^25 + 60*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 68*x^18 + 79*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 81*x^9 + 52*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 76*x^2 + 65*x + 28, x^93 + 74*x^91 + 40*x^90 + 35*x^89 + 40*x^88 + 68*x^87 + 112*x^86 + x^85 + 48*x^84 + 102*x^83 + 56*x^82 + 43*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 93*x^73 + 56*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 104*x^66 + 29*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 47*x^25 + 72*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 24*x^18 + 119*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 89*x^9 + 88*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 72*x^2 + 121*x + 8, x^93 + 74*x^91 + 96*x^90 + 3*x^89 + 96*x^88 + 68*x^87 + 65*x^85 + 102*x^83 + 96*x^82 + 75*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 125*x^73 + 32*x^72 + 116*x^71 + 71*x^69 + 114*x^67 + 32*x^66 + 125*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 15*x^25 + 96*x^24 + 116*x^23 + 101*x^21 + 30*x^19 + 96*x^18 + 23*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 121*x^9 + 32*x^8 + 68*x^7 + 91*x^5 + 106*x^3 + 32*x^2 + 89*x + 32, x^93 + 74*x^91 + 8*x^90 + 99*x^89 + 104*x^88 + 68*x^87 + 48*x^86 + x^85 + 48*x^84 + 102*x^83 + 88*x^82 + 107*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 29*x^73 + 120*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 72*x^66 + 93*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 111*x^25 + 8*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 56*x^18 + 55*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 25*x^9 + 24*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 40*x^2 + 57*x + 72, x^93 + 74*x^91 + 60*x^90 + 43*x^89 + 76*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 20*x^82 + 99*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 117*x^73 + 68*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 92*x^66 + 69*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 87*x^25 + 60*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 36*x^18 + 15*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 17*x^9 + 52*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 108*x^2 + x + 28, x^93 + 74*x^91 + 96*x^90 + 83*x^89 + 80*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 102*x^83 + 32*x^82 + 59*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 109*x^73 + 112*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 114*x^67 + 96*x^66 + 77*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 31*x^25 + 16*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 30*x^19 + 32*x^18 + 71*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 41*x^9 + 48*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 106*x^3 + 96*x^2 + 105*x + 16, x^93 + 74*x^91 + 8*x^90 + 83*x^89 + 88*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 24*x^82 + 59*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 109*x^73 + 72*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 8*x^66 + 77*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 31*x^25 + 56*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 120*x^18 + 71*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 41*x^9 + 40*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 104*x^2 + 105*x + 56, x^93 + 74*x^91 + 52*x^90 + 59*x^89 + 52*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 124*x^82 + 19*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 37*x^73 + 60*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 84*x^66 + 85*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 39*x^25 + 68*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 44*x^18 + 127*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + x^9 + 76*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 4*x^2 + 81*x + 36, x^93 + 74*x^91 + 32*x^90 + 3*x^89 + 68*x^87 + 65*x^85 + 64*x^84 + 102*x^83 + 32*x^82 + 75*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 125*x^73 + 116*x^71 + 71*x^69 + 64*x^68 + 114*x^67 + 96*x^66 + 125*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 15*x^25 + 116*x^23 + 101*x^21 + 64*x^20 + 30*x^19 + 32*x^18 + 23*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 121*x^9 + 68*x^7 + 91*x^5 + 64*x^4 + 106*x^3 + 96*x^2 + 89*x + 64, x^93 + 74*x^91 + 44*x^90 + 11*x^89 + 28*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 100*x^82 + 3*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 21*x^73 + 52*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 76*x^66 + 37*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 55*x^25 + 76*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 52*x^18 + 47*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 49*x^9 + 100*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 28*x^2 + 97*x + 44, x^93 + 74*x^91 + 32*x^90 + 3*x^89 + 96*x^88 + 4*x^87 + 64*x^86 + x^85 + 64*x^84 + 38*x^83 + 96*x^82 + 11*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 125*x^73 + 32*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 50*x^67 + 32*x^66 + 61*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 15*x^25 + 96*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 94*x^19 + 96*x^18 + 87*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 121*x^9 + 32*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 42*x^3 + 32*x^2 + 25*x + 96, x^93 + 74*x^91 + 4*x^90 + 27*x^89 + 4*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 108*x^82 + 51*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 69*x^73 + 44*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 36*x^66 + 53*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 7*x^25 + 84*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 92*x^18 + 31*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 33*x^9 + 124*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 20*x^2 + 49*x + 52, x^93 + 74*x^91 + 28*x^90 + 123*x^89 + 28*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 52*x^82 + 19*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 101*x^73 + 52*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 60*x^66 + 85*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 103*x^25 + 76*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 68*x^18 + 127*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 65*x^9 + 100*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 76*x^2 + 81*x + 44, x^93 + 74*x^91 + 108*x^90 + 91*x^89 + 76*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 100*x^82 + 115*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 5*x^73 + 68*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 76*x^66 + 117*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 71*x^25 + 60*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 52*x^18 + 95*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 97*x^9 + 52*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 28*x^2 + 113*x + 92, x^93 + 74*x^91 + 48*x^90 + 115*x^89 + 32*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 38*x^83 + 80*x^82 + 91*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 77*x^73 + 96*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 50*x^67 + 112*x^66 + 45*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 63*x^25 + 32*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 94*x^19 + 16*x^18 + 103*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 9*x^9 + 96*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 42*x^3 + 48*x^2 + 73*x + 96, x^93 + 74*x^91 + 99*x^89 + 64*x^88 + 68*x^87 + 64*x^86 + x^85 + 64*x^84 + 102*x^83 + 64*x^82 + 107*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 29*x^73 + 64*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 114*x^67 + 64*x^66 + 93*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 111*x^25 + 64*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 30*x^19 + 64*x^18 + 55*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 25*x^9 + 64*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 106*x^3 + 64*x^2 + 57*x, x^93 + 74*x^91 + 64*x^90 + 115*x^89 + 112*x^88 + 68*x^87 + 97*x^85 + 32*x^84 + 102*x^83 + 64*x^82 + 27*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 77*x^73 + 80*x^72 + 116*x^71 + 103*x^69 + 32*x^68 + 114*x^67 + 64*x^66 + 109*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 63*x^25 + 48*x^24 + 116*x^23 + 5*x^21 + 32*x^20 + 30*x^19 + 64*x^18 + 39*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 9*x^9 + 16*x^8 + 68*x^7 + 123*x^5 + 32*x^4 + 106*x^3 + 64*x^2 + 9*x + 48, x^93 + 74*x^91 + 56*x^90 + 51*x^89 + 72*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 104*x^82 + 27*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 13*x^73 + 24*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 120*x^66 + 109*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 127*x^25 + 104*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 8*x^18 + 39*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 73*x^9 + 56*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 24*x^2 + 9*x + 40, x^93 + 74*x^91 + 100*x^90 + 43*x^89 + 116*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 76*x^82 + 99*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 117*x^73 + 124*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 68*x^66 + 69*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 87*x^25 + 4*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 60*x^18 + 15*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 17*x^9 + 12*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 52*x^2 + x + 36, x^93 + 74*x^91 + 24*x^90 + 3*x^89 + 120*x^88 + 4*x^87 + 80*x^86 + x^85 + 80*x^84 + 38*x^83 + 72*x^82 + 11*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 125*x^73 + 40*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 24*x^66 + 61*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 15*x^25 + 88*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 104*x^18 + 87*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 121*x^9 + 8*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 56*x^2 + 25*x + 88, x^93 + 74*x^91 + 20*x^90 + 91*x^89 + 52*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 28*x^82 + 115*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 5*x^73 + 60*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 52*x^66 + 117*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 71*x^25 + 68*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 76*x^18 + 95*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 97*x^9 + 76*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 100*x^2 + 113*x + 36, x^93 + 74*x^91 + 96*x^90 + 35*x^89 + 64*x^88 + 68*x^87 + x^85 + 64*x^84 + 102*x^83 + 96*x^82 + 43*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 93*x^73 + 64*x^72 + 116*x^71 + 7*x^69 + 64*x^68 + 114*x^67 + 32*x^66 + 29*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 47*x^25 + 64*x^24 + 116*x^23 + 37*x^21 + 64*x^20 + 30*x^19 + 96*x^18 + 119*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 89*x^9 + 64*x^8 + 68*x^7 + 27*x^5 + 64*x^4 + 106*x^3 + 32*x^2 + 121*x, x^93 + 74*x^91 + 12*x^90 + 107*x^89 + 60*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 4*x^82 + 35*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 53*x^73 + 20*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 44*x^66 + 5*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 23*x^25 + 108*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 84*x^18 + 79*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 81*x^9 + 68*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 124*x^2 + 65*x + 76, x^93 + 74*x^91 + 16*x^90 + 35*x^89 + 112*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 48*x^82 + 107*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 93*x^73 + 80*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 16*x^66 + 93*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 47*x^25 + 48*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 112*x^18 + 55*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 89*x^9 + 16*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 80*x^2 + 57*x + 48, x^93 + 74*x^91 + 36*x^90 + 91*x^89 + 36*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 76*x^82 + 115*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 5*x^73 + 12*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 68*x^66 + 117*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 71*x^25 + 116*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 60*x^18 + 95*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 97*x^9 + 92*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 52*x^2 + 113*x + 84, x^93 + 74*x^91 + 72*x^90 + 67*x^89 + 8*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 24*x^82 + 11*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 61*x^73 + 88*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 8*x^66 + 61*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 79*x^25 + 40*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 120*x^18 + 87*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 57*x^9 + 120*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 104*x^2 + 25*x + 104, x^93 + 74*x^91 + 28*x^90 + 11*x^89 + 108*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 116*x^82 + 67*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 21*x^73 + 36*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 124*x^66 + 101*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 55*x^25 + 92*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 4*x^18 + 111*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 49*x^9 + 20*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 12*x^2 + 33*x + 124, x^93 + 74*x^91 + 12*x^90 + 91*x^89 + 44*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 68*x^82 + 115*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 5*x^73 + 100*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 108*x^66 + 117*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 71*x^25 + 28*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 20*x^18 + 95*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 97*x^9 + 84*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 60*x^2 + 113*x + 60, x^93 + 74*x^91 + 8*x^90 + 19*x^89 + 120*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 24*x^82 + 123*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 45*x^73 + 40*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 8*x^66 + 13*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 95*x^25 + 88*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 120*x^18 + 7*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 105*x^9 + 8*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 104*x^2 + 41*x + 88, x^93 + 74*x^91 + 100*x^90 + 75*x^89 + 20*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 76*x^82 + 67*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 85*x^73 + 92*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 68*x^66 + 101*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 119*x^25 + 36*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 60*x^18 + 111*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 113*x^9 + 108*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 52*x^2 + 33*x + 68, x^93 + 74*x^91 + 112*x^90 + 19*x^89 + 96*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 38*x^83 + 16*x^82 + 59*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 45*x^73 + 32*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 50*x^67 + 48*x^66 + 77*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 95*x^25 + 96*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 94*x^19 + 80*x^18 + 71*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 105*x^9 + 32*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 42*x^3 + 112*x^2 + 105*x + 32, x^93 + 74*x^91 + 68*x^90 + 27*x^89 + 100*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 44*x^82 + 51*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 69*x^73 + 76*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 100*x^66 + 53*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 7*x^25 + 52*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 28*x^18 + 31*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 33*x^9 + 28*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 84*x^2 + 49*x + 20, x^93 + 74*x^91 + 92*x^90 + 59*x^89 + 60*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 52*x^82 + 19*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 37*x^73 + 20*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 60*x^66 + 85*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 39*x^25 + 108*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 68*x^18 + 127*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + x^9 + 68*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 76*x^2 + 81*x + 12, x^93 + 74*x^91 + 32*x^90 + 51*x^89 + 48*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 102*x^83 + 96*x^82 + 91*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 13*x^73 + 16*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 114*x^67 + 32*x^66 + 45*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 127*x^25 + 112*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 30*x^19 + 96*x^18 + 103*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 73*x^9 + 80*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 106*x^3 + 32*x^2 + 73*x + 112, x^93 + 74*x^91 + 88*x^90 + 19*x^89 + 72*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 8*x^82 + 123*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 45*x^73 + 24*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 88*x^66 + 13*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 95*x^25 + 104*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 40*x^18 + 7*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 105*x^9 + 56*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 120*x^2 + 41*x + 104, x^93 + 74*x^91 + 100*x^90 + 91*x^89 + 4*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 76*x^82 + 51*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 5*x^73 + 44*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 68*x^66 + 53*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 71*x^25 + 84*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 60*x^18 + 31*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 97*x^9 + 124*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 52*x^2 + 49*x + 116, x^93 + 74*x^91 + 96*x^90 + 51*x^89 + 48*x^88 + 4*x^87 + 33*x^85 + 96*x^84 + 38*x^83 + 96*x^82 + 27*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 13*x^73 + 16*x^72 + 52*x^71 + 39*x^69 + 96*x^68 + 50*x^67 + 32*x^66 + 109*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 127*x^25 + 112*x^24 + 52*x^23 + 69*x^21 + 96*x^20 + 94*x^19 + 96*x^18 + 39*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 73*x^9 + 80*x^8 + 4*x^7 + 59*x^5 + 96*x^4 + 42*x^3 + 32*x^2 + 9*x + 48, x^93 + 74*x^91 + 120*x^90 + 115*x^89 + 72*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 104*x^82 + 27*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 77*x^73 + 24*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 120*x^66 + 109*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 63*x^25 + 104*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 8*x^18 + 39*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 9*x^9 + 56*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 24*x^2 + 9*x + 104, x^93 + 74*x^91 + 28*x^90 + 27*x^89 + 60*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 116*x^82 + 51*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 69*x^73 + 20*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 124*x^66 + 53*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 7*x^25 + 108*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 4*x^18 + 31*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 33*x^9 + 68*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 12*x^2 + 49*x + 12, x^93 + 74*x^91 + 35*x^89 + 96*x^88 + 4*x^87 + 65*x^85 + 64*x^84 + 38*x^83 + 107*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 93*x^73 + 32*x^72 + 52*x^71 + 71*x^69 + 64*x^68 + 50*x^67 + 93*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 47*x^25 + 96*x^24 + 52*x^23 + 101*x^21 + 64*x^20 + 94*x^19 + 55*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 89*x^9 + 32*x^8 + 4*x^7 + 91*x^5 + 64*x^4 + 42*x^3 + 57*x + 96, x^93 + 74*x^91 + 112*x^90 + 67*x^89 + 16*x^88 + 4*x^87 + 32*x^86 + x^85 + 96*x^84 + 38*x^83 + 80*x^82 + 75*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 61*x^73 + 48*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 112*x^66 + 125*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 79*x^25 + 80*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 16*x^18 + 23*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 57*x^9 + 112*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 48*x^2 + 89*x + 80, x^93 + 74*x^91 + 64*x^90 + 51*x^89 + 48*x^88 + 68*x^87 + 97*x^85 + 32*x^84 + 102*x^83 + 64*x^82 + 91*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 13*x^73 + 16*x^72 + 116*x^71 + 103*x^69 + 32*x^68 + 114*x^67 + 64*x^66 + 45*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 127*x^25 + 112*x^24 + 116*x^23 + 5*x^21 + 32*x^20 + 30*x^19 + 64*x^18 + 103*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 73*x^9 + 80*x^8 + 68*x^7 + 123*x^5 + 32*x^4 + 106*x^3 + 64*x^2 + 73*x + 112, x^93 + 74*x^91 + 112*x^90 + 19*x^89 + 32*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 38*x^83 + 16*x^82 + 59*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 45*x^73 + 96*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 50*x^67 + 48*x^66 + 77*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 95*x^25 + 32*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 94*x^19 + 80*x^18 + 71*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 105*x^9 + 96*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 42*x^3 + 112*x^2 + 105*x + 96, x^93 + 74*x^91 + 68*x^90 + 107*x^89 + 116*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 108*x^82 + 35*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 53*x^73 + 124*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 36*x^66 + 5*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 23*x^25 + 4*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 92*x^18 + 79*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 81*x^9 + 12*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 20*x^2 + 65*x + 36, x^93 + 74*x^91 + 104*x^90 + 3*x^89 + 8*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 120*x^82 + 75*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 125*x^73 + 88*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 40*x^66 + 125*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 15*x^25 + 40*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 88*x^18 + 23*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 121*x^9 + 120*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 8*x^2 + 89*x + 104, x^93 + 74*x^91 + 4*x^90 + 107*x^89 + 52*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 44*x^82 + 35*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 53*x^73 + 60*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 100*x^66 + 5*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 23*x^25 + 68*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 28*x^18 + 79*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 81*x^9 + 76*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 84*x^2 + 65*x + 100, x^93 + 74*x^91 + 80*x^90 + 83*x^89 + 68*x^87 + 96*x^86 + 33*x^85 + 102*x^83 + 112*x^82 + 59*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 109*x^73 + 116*x^71 + 96*x^70 + 39*x^69 + 114*x^67 + 80*x^66 + 77*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 31*x^25 + 116*x^23 + 96*x^22 + 69*x^21 + 30*x^19 + 48*x^18 + 71*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 41*x^9 + 68*x^7 + 96*x^6 + 59*x^5 + 106*x^3 + 16*x^2 + 105*x, x^93 + 74*x^91 + 12*x^90 + 11*x^89 + 124*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 68*x^82 + 67*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 21*x^73 + 84*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 108*x^66 + 101*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 55*x^25 + 44*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 20*x^18 + 111*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 49*x^9 + 4*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 60*x^2 + 33*x + 76, x^93 + 74*x^91 + 112*x^90 + 3*x^89 + 16*x^88 + 4*x^87 + 32*x^86 + x^85 + 96*x^84 + 38*x^83 + 80*x^82 + 11*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 125*x^73 + 48*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 112*x^66 + 61*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 15*x^25 + 80*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 16*x^18 + 87*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 121*x^9 + 112*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 48*x^2 + 25*x + 80, x^93 + 74*x^91 + 88*x^90 + 35*x^89 + 56*x^88 + 68*x^87 + 16*x^86 + x^85 + 16*x^84 + 102*x^83 + 72*x^82 + 43*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 93*x^73 + 104*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 24*x^66 + 29*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 47*x^25 + 24*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 104*x^18 + 119*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 89*x^9 + 72*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 56*x^2 + 121*x + 88, x^93 + 74*x^91 + 36*x^90 + 91*x^89 + 100*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 76*x^82 + 115*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 5*x^73 + 76*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 68*x^66 + 117*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 71*x^25 + 52*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 60*x^18 + 95*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 97*x^9 + 28*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 52*x^2 + 113*x + 20, x^93 + 74*x^91 + 96*x^90 + 83*x^89 + 112*x^88 + 4*x^87 + 97*x^85 + 96*x^84 + 38*x^83 + 96*x^82 + 123*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 109*x^73 + 80*x^72 + 52*x^71 + 103*x^69 + 96*x^68 + 50*x^67 + 32*x^66 + 13*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 31*x^25 + 48*x^24 + 52*x^23 + 5*x^21 + 96*x^20 + 94*x^19 + 96*x^18 + 7*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 41*x^9 + 16*x^8 + 4*x^7 + 123*x^5 + 96*x^4 + 42*x^3 + 32*x^2 + 41*x + 112, x^93 + 74*x^91 + 88*x^90 + 115*x^89 + 40*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 72*x^82 + 91*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 77*x^73 + 56*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 24*x^66 + 45*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 63*x^25 + 72*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 104*x^18 + 103*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 9*x^9 + 88*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 56*x^2 + 73*x + 8, x^93 + 74*x^91 + 120*x^90 + 51*x^89 + 40*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 40*x^82 + 27*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 13*x^73 + 56*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 56*x^66 + 109*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 127*x^25 + 72*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 72*x^18 + 39*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 73*x^9 + 88*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 88*x^2 + 9*x + 8, x^93 + 74*x^91 + 124*x^90 + 43*x^89 + 76*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 84*x^82 + 99*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 117*x^73 + 68*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 28*x^66 + 69*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 87*x^25 + 60*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 100*x^18 + 15*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 17*x^9 + 52*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 44*x^2 + x + 28, x^93 + 74*x^91 + 48*x^90 + 83*x^89 + 68*x^87 + 32*x^86 + 33*x^85 + 102*x^83 + 16*x^82 + 59*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 109*x^73 + 116*x^71 + 32*x^70 + 39*x^69 + 114*x^67 + 48*x^66 + 77*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 31*x^25 + 116*x^23 + 32*x^22 + 69*x^21 + 30*x^19 + 80*x^18 + 71*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 41*x^9 + 68*x^7 + 32*x^6 + 59*x^5 + 106*x^3 + 112*x^2 + 105*x, x^93 + 74*x^91 + 64*x^90 + 35*x^89 + 32*x^88 + 68*x^87 + 64*x^86 + x^85 + 102*x^83 + 43*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 93*x^73 + 96*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 114*x^67 + 29*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 47*x^25 + 32*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 30*x^19 + 119*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 89*x^9 + 96*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 106*x^3 + 121*x + 96, x^93 + 74*x^91 + 16*x^90 + 3*x^89 + 112*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 112*x^82 + 75*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 125*x^73 + 80*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 80*x^66 + 125*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 15*x^25 + 48*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 48*x^18 + 23*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 121*x^9 + 16*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 16*x^2 + 89*x + 112, x^93 + 74*x^91 + 12*x^90 + 27*x^89 + 76*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 68*x^82 + 51*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 69*x^73 + 68*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 108*x^66 + 53*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 7*x^25 + 60*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 20*x^18 + 31*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 33*x^9 + 52*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 60*x^2 + 49*x + 92, x^93 + 74*x^91 + 80*x^90 + 3*x^89 + 48*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 48*x^82 + 75*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 125*x^73 + 16*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 16*x^66 + 125*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 15*x^25 + 112*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 112*x^18 + 23*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 121*x^9 + 80*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 80*x^2 + 89*x + 48, x^93 + 74*x^91 + 4*x^90 + 59*x^89 + 4*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 108*x^82 + 19*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 37*x^73 + 44*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 36*x^66 + 85*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 39*x^25 + 84*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 92*x^18 + 127*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + x^9 + 124*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 20*x^2 + 81*x + 52, x^93 + 74*x^91 + 24*x^90 + 67*x^89 + 56*x^88 + 4*x^87 + 80*x^86 + x^85 + 80*x^84 + 38*x^83 + 72*x^82 + 75*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 61*x^73 + 104*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 24*x^66 + 125*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 79*x^25 + 24*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 104*x^18 + 23*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 57*x^9 + 72*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 56*x^2 + 89*x + 24, x^93 + 74*x^91 + 60*x^90 + 91*x^89 + 92*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 20*x^82 + 51*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 5*x^73 + 116*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 92*x^66 + 53*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 71*x^25 + 12*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 36*x^18 + 31*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 97*x^9 + 36*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 108*x^2 + 49*x + 108, x^93 + 74*x^91 + 76*x^90 + 91*x^89 + 12*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 68*x^82 + 51*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 5*x^73 + 4*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 108*x^66 + 53*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 71*x^25 + 124*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 20*x^18 + 31*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 97*x^9 + 116*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 60*x^2 + 49*x + 92, x^93 + 74*x^91 + 120*x^90 + 19*x^89 + 8*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 40*x^82 + 59*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 45*x^73 + 88*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 56*x^66 + 77*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 95*x^25 + 40*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 72*x^18 + 71*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 105*x^9 + 120*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 88*x^2 + 105*x + 104, x^93 + 74*x^91 + 64*x^90 + 35*x^89 + 64*x^88 + 4*x^87 + 65*x^85 + 38*x^83 + 64*x^82 + 107*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 93*x^73 + 64*x^72 + 52*x^71 + 71*x^69 + 50*x^67 + 64*x^66 + 93*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 47*x^25 + 64*x^24 + 52*x^23 + 101*x^21 + 94*x^19 + 64*x^18 + 55*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 89*x^9 + 64*x^8 + 4*x^7 + 91*x^5 + 42*x^3 + 64*x^2 + 57*x + 64, x^93 + 74*x^91 + 20*x^90 + 123*x^89 + 84*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 92*x^82 + 19*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 101*x^73 + 28*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 116*x^66 + 85*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 103*x^25 + 100*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 12*x^18 + 127*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 65*x^9 + 44*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 36*x^2 + 81*x + 4, x^93 + 74*x^91 + 52*x^90 + 59*x^89 + 20*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 60*x^82 + 83*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 37*x^73 + 92*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 20*x^66 + 21*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 39*x^25 + 36*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 108*x^18 + 63*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + x^9 + 108*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 68*x^2 + 17*x + 68, x^93 + 74*x^91 + 56*x^90 + 3*x^89 + 120*x^88 + 4*x^87 + 16*x^86 + x^85 + 80*x^84 + 38*x^83 + 40*x^82 + 11*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 125*x^73 + 40*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 56*x^66 + 61*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 15*x^25 + 88*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 72*x^18 + 87*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 121*x^9 + 8*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 88*x^2 + 25*x + 88, x^93 + 74*x^91 + 20*x^90 + 123*x^89 + 116*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 92*x^82 + 19*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 101*x^73 + 124*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 116*x^66 + 85*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 103*x^25 + 4*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 12*x^18 + 127*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 65*x^9 + 12*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 36*x^2 + 81*x + 36, x^93 + 74*x^91 + 16*x^90 + 99*x^89 + 48*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 48*x^82 + 43*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 29*x^73 + 16*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 16*x^66 + 29*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 111*x^25 + 112*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 112*x^18 + 119*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 25*x^9 + 80*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 80*x^2 + 121*x + 112, x^93 + 74*x^91 + 84*x^90 + 11*x^89 + 36*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 92*x^82 + 67*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 21*x^73 + 12*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 116*x^66 + 101*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 55*x^25 + 116*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 12*x^18 + 111*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 49*x^9 + 92*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 36*x^2 + 33*x + 84, x^93 + 74*x^91 + 20*x^90 + 11*x^89 + 100*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 92*x^82 + 3*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 21*x^73 + 76*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 116*x^66 + 37*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 55*x^25 + 52*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 12*x^18 + 47*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 49*x^9 + 28*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 36*x^2 + 97*x + 84, x^93 + 74*x^91 + 100*x^90 + 11*x^89 + 84*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 12*x^82 + 67*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 21*x^73 + 28*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 4*x^66 + 101*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 55*x^25 + 100*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 124*x^18 + 111*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 49*x^9 + 44*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 116*x^2 + 33*x + 68, x^93 + 74*x^91 + 32*x^90 + 83*x^89 + 48*x^88 + 4*x^87 + 97*x^85 + 96*x^84 + 38*x^83 + 32*x^82 + 123*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 109*x^73 + 16*x^72 + 52*x^71 + 103*x^69 + 96*x^68 + 50*x^67 + 96*x^66 + 13*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 31*x^25 + 112*x^24 + 52*x^23 + 5*x^21 + 96*x^20 + 94*x^19 + 32*x^18 + 7*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 41*x^9 + 80*x^8 + 4*x^7 + 123*x^5 + 96*x^4 + 42*x^3 + 96*x^2 + 41*x + 48, x^93 + 74*x^91 + 40*x^90 + 67*x^89 + 8*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 56*x^82 + 11*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 61*x^73 + 88*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 104*x^66 + 61*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 79*x^25 + 40*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 24*x^18 + 87*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 57*x^9 + 120*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 72*x^2 + 25*x + 104, x^93 + 74*x^91 + 108*x^90 + 59*x^89 + 76*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 36*x^82 + 83*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 37*x^73 + 68*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 12*x^66 + 21*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 39*x^25 + 60*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 116*x^18 + 63*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + x^9 + 52*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 92*x^2 + 17*x + 28, x^93 + 74*x^91 + 60*x^90 + 75*x^89 + 76*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 84*x^82 + 3*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 85*x^73 + 68*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 28*x^66 + 37*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 119*x^25 + 60*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 100*x^18 + 47*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 113*x^9 + 52*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 44*x^2 + 97*x + 92, x^93 + 74*x^91 + 56*x^90 + 99*x^89 + 24*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 40*x^82 + 43*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 29*x^73 + 8*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 56*x^66 + 29*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 111*x^25 + 120*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 72*x^18 + 119*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 25*x^9 + 104*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 88*x^2 + 121*x + 120, x^93 + 74*x^91 + 84*x^90 + 123*x^89 + 52*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 28*x^82 + 19*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 101*x^73 + 60*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 52*x^66 + 85*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 103*x^25 + 68*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 76*x^18 + 127*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 65*x^9 + 76*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 100*x^2 + 81*x + 100, x^93 + 74*x^91 + 60*x^90 + 11*x^89 + 12*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 20*x^82 + 3*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 21*x^73 + 4*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 92*x^66 + 37*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 55*x^25 + 124*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 36*x^18 + 47*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 49*x^9 + 116*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 108*x^2 + 97*x + 92, x^93 + 74*x^91 + 120*x^90 + 3*x^89 + 24*x^88 + 4*x^87 + 16*x^86 + x^85 + 16*x^84 + 38*x^83 + 104*x^82 + 11*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 125*x^73 + 8*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 120*x^66 + 61*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 15*x^25 + 120*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 8*x^18 + 87*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 121*x^9 + 104*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 24*x^2 + 25*x + 120, x^93 + 74*x^91 + 115*x^89 + 112*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 38*x^83 + 64*x^82 + 91*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 77*x^73 + 80*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 50*x^67 + 64*x^66 + 45*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 63*x^25 + 48*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 94*x^19 + 64*x^18 + 103*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 9*x^9 + 16*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 42*x^3 + 64*x^2 + 73*x + 112, x^93 + 74*x^91 + 52*x^90 + 107*x^89 + 4*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 60*x^82 + 35*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 53*x^73 + 44*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 20*x^66 + 5*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 23*x^25 + 84*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 108*x^18 + 79*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 81*x^9 + 124*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 68*x^2 + 65*x + 116, x^93 + 74*x^91 + 24*x^90 + 35*x^89 + 88*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 72*x^82 + 107*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 93*x^73 + 72*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 24*x^66 + 93*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 47*x^25 + 56*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 104*x^18 + 55*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 89*x^9 + 40*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 56*x^2 + 57*x + 56, x^93 + 74*x^91 + 108*x^90 + 75*x^89 + 28*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 100*x^82 + 3*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 85*x^73 + 52*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 76*x^66 + 37*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 119*x^25 + 76*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 52*x^18 + 47*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 113*x^9 + 100*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 28*x^2 + 97*x + 108, x^93 + 74*x^91 + 112*x^90 + 51*x^89 + 64*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 102*x^83 + 80*x^82 + 91*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 13*x^73 + 64*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 114*x^67 + 112*x^66 + 45*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 127*x^25 + 64*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 30*x^19 + 16*x^18 + 103*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 73*x^9 + 64*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 106*x^3 + 48*x^2 + 73*x + 64, x^93 + 74*x^91 + 84*x^90 + 75*x^89 + 100*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 92*x^82 + 3*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 85*x^73 + 76*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 116*x^66 + 37*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 119*x^25 + 52*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 12*x^18 + 47*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 113*x^9 + 28*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 36*x^2 + 97*x + 20, x^93 + 74*x^91 + 8*x^90 + 35*x^89 + 104*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 24*x^82 + 107*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 93*x^73 + 120*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 8*x^66 + 93*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 47*x^25 + 8*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 120*x^18 + 55*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 89*x^9 + 24*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 104*x^2 + 57*x + 8, x^93 + 74*x^91 + 108*x^90 + 75*x^89 + 92*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 36*x^82 + 67*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 85*x^73 + 116*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 12*x^66 + 101*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 119*x^25 + 12*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 116*x^18 + 111*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 113*x^9 + 36*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 92*x^2 + 33*x + 108, x^93 + 74*x^91 + 67*x^89 + 96*x^88 + 4*x^87 + x^85 + 64*x^84 + 38*x^83 + 75*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 61*x^73 + 32*x^72 + 52*x^71 + 7*x^69 + 64*x^68 + 50*x^67 + 125*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 79*x^25 + 96*x^24 + 52*x^23 + 37*x^21 + 64*x^20 + 94*x^19 + 23*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 57*x^9 + 32*x^8 + 4*x^7 + 27*x^5 + 64*x^4 + 42*x^3 + 89*x + 96, x^93 + 74*x^91 + 12*x^90 + 123*x^89 + 12*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 68*x^82 + 83*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 101*x^73 + 4*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 108*x^66 + 21*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 103*x^25 + 124*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 20*x^18 + 63*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 65*x^9 + 116*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 60*x^2 + 17*x + 28, x^93 + 74*x^91 + 120*x^90 + 99*x^89 + 24*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 104*x^82 + 43*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 29*x^73 + 8*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 120*x^66 + 29*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 111*x^25 + 120*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 8*x^18 + 119*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 25*x^9 + 104*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 24*x^2 + 121*x + 120, x^93 + 74*x^91 + 88*x^90 + 83*x^89 + 40*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 72*x^82 + 123*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 109*x^73 + 56*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 24*x^66 + 13*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 31*x^25 + 72*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 104*x^18 + 7*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 41*x^9 + 88*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 56*x^2 + 41*x + 8, x^93 + 74*x^91 + 100*x^90 + 107*x^89 + 116*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 12*x^82 + 99*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 53*x^73 + 124*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 4*x^66 + 69*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 23*x^25 + 4*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 124*x^18 + 15*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 81*x^9 + 12*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 116*x^2 + x + 100, x^93 + 74*x^91 + 76*x^90 + 11*x^89 + 124*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 68*x^82 + 3*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 21*x^73 + 84*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 108*x^66 + 37*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 55*x^25 + 44*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 20*x^18 + 47*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 49*x^9 + 4*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 60*x^2 + 97*x + 12, x^93 + 74*x^91 + 16*x^90 + 67*x^89 + 16*x^88 + 4*x^87 + 96*x^86 + x^85 + 96*x^84 + 38*x^83 + 48*x^82 + 75*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 61*x^73 + 48*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 16*x^66 + 125*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 79*x^25 + 80*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 112*x^18 + 23*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 57*x^9 + 112*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 80*x^2 + 89*x + 80, x^93 + 74*x^91 + 20*x^90 + 11*x^89 + 68*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 92*x^82 + 3*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 21*x^73 + 108*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 116*x^66 + 37*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 55*x^25 + 20*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 12*x^18 + 47*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 49*x^9 + 60*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 36*x^2 + 97*x + 52, x^93 + 74*x^91 + 56*x^90 + 51*x^89 + 40*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 104*x^82 + 27*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 13*x^73 + 56*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 120*x^66 + 109*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 127*x^25 + 72*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 8*x^18 + 39*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 73*x^9 + 88*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 24*x^2 + 9*x + 8, x^93 + 74*x^91 + 56*x^90 + 19*x^89 + 40*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 104*x^82 + 59*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 45*x^73 + 56*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 120*x^66 + 77*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 95*x^25 + 72*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 8*x^18 + 71*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 105*x^9 + 88*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 24*x^2 + 105*x + 8, x^93 + 74*x^91 + 28*x^90 + 43*x^89 + 12*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 116*x^82 + 35*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 117*x^73 + 4*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 124*x^66 + 5*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 87*x^25 + 124*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 4*x^18 + 79*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 17*x^9 + 116*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 12*x^2 + 65*x + 28, x^93 + 74*x^91 + 16*x^90 + 35*x^89 + 80*x^88 + 68*x^87 + 32*x^86 + x^85 + 32*x^84 + 102*x^83 + 112*x^82 + 43*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 93*x^73 + 112*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 80*x^66 + 29*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 47*x^25 + 16*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 48*x^18 + 119*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 89*x^9 + 48*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 16*x^2 + 121*x + 80, x^93 + 74*x^91 + 84*x^90 + 43*x^89 + 68*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 92*x^82 + 35*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 117*x^73 + 108*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 116*x^66 + 5*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 87*x^25 + 20*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 12*x^18 + 79*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 17*x^9 + 60*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 36*x^2 + 65*x + 116, x^93 + 74*x^91 + 112*x^90 + 3*x^89 + 16*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 16*x^82 + 75*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 125*x^73 + 48*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 48*x^66 + 125*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 15*x^25 + 80*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 80*x^18 + 23*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 121*x^9 + 112*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 112*x^2 + 89*x + 16, x^93 + 74*x^91 + 12*x^90 + 27*x^89 + 44*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 68*x^82 + 51*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 69*x^73 + 100*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 108*x^66 + 53*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 7*x^25 + 28*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 20*x^18 + 31*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 33*x^9 + 84*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 60*x^2 + 49*x + 60, x^93 + 74*x^91 + 88*x^90 + 67*x^89 + 56*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 72*x^82 + 11*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 61*x^73 + 104*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 24*x^66 + 61*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 79*x^25 + 24*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 104*x^18 + 87*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 57*x^9 + 72*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 56*x^2 + 25*x + 88, x^93 + 74*x^91 + 20*x^90 + 59*x^89 + 52*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 92*x^82 + 83*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 37*x^73 + 60*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 116*x^66 + 21*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 39*x^25 + 68*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 12*x^18 + 63*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + x^9 + 76*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 36*x^2 + 17*x + 100, x^93 + 74*x^91 + 104*x^90 + 19*x^89 + 56*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 120*x^82 + 59*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 45*x^73 + 104*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 40*x^66 + 77*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 95*x^25 + 24*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 88*x^18 + 71*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 105*x^9 + 72*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 8*x^2 + 105*x + 88, x^93 + 74*x^91 + 4*x^90 + 59*x^89 + 100*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 108*x^82 + 19*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 37*x^73 + 76*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 36*x^66 + 85*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 39*x^25 + 52*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 92*x^18 + 127*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + x^9 + 28*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 20*x^2 + 81*x + 20, x^93 + 74*x^91 + 20*x^90 + 75*x^89 + 36*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 28*x^82 + 3*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 85*x^73 + 12*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 52*x^66 + 37*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 119*x^25 + 116*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 76*x^18 + 47*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 113*x^9 + 92*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 100*x^2 + 97*x + 84, x^93 + 74*x^91 + 12*x^90 + 107*x^89 + 92*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 68*x^82 + 99*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 53*x^73 + 116*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 108*x^66 + 69*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 23*x^25 + 12*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 20*x^18 + 15*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 81*x^9 + 36*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 60*x^2 + x + 44, x^93 + 74*x^91 + 8*x^90 + 51*x^89 + 120*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 88*x^82 + 27*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 13*x^73 + 40*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 72*x^66 + 109*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 127*x^25 + 88*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 56*x^18 + 39*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 73*x^9 + 8*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 40*x^2 + 9*x + 24, x^93 + 74*x^91 + 104*x^90 + 67*x^89 + 40*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 120*x^82 + 11*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 61*x^73 + 56*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 40*x^66 + 61*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 79*x^25 + 72*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 88*x^18 + 87*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 57*x^9 + 88*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 8*x^2 + 25*x + 8, x^93 + 74*x^91 + 32*x^90 + 51*x^89 + 80*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 102*x^83 + 96*x^82 + 91*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 13*x^73 + 112*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 114*x^67 + 32*x^66 + 45*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 127*x^25 + 16*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 30*x^19 + 96*x^18 + 103*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 73*x^9 + 48*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 106*x^3 + 32*x^2 + 73*x + 16, x^93 + 74*x^91 + 104*x^90 + 67*x^89 + 104*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 120*x^82 + 11*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 61*x^73 + 120*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 40*x^66 + 61*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 79*x^25 + 8*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 88*x^18 + 87*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 57*x^9 + 24*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 8*x^2 + 25*x + 72, x^93 + 74*x^91 + 100*x^90 + 27*x^89 + 68*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 12*x^82 + 51*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 69*x^73 + 108*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 4*x^66 + 53*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 7*x^25 + 20*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 124*x^18 + 31*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 33*x^9 + 60*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 116*x^2 + 49*x + 116, x^93 + 74*x^91 + 76*x^90 + 123*x^89 + 12*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 68*x^82 + 19*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 101*x^73 + 4*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 108*x^66 + 85*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 103*x^25 + 124*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 20*x^18 + 127*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 65*x^9 + 116*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 60*x^2 + 81*x + 92, x^93 + 74*x^91 + 96*x^90 + 51*x^89 + 80*x^88 + 4*x^87 + 33*x^85 + 32*x^84 + 38*x^83 + 96*x^82 + 27*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 13*x^73 + 112*x^72 + 52*x^71 + 39*x^69 + 32*x^68 + 50*x^67 + 32*x^66 + 109*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 127*x^25 + 16*x^24 + 52*x^23 + 69*x^21 + 32*x^20 + 94*x^19 + 96*x^18 + 39*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 73*x^9 + 48*x^8 + 4*x^7 + 59*x^5 + 32*x^4 + 42*x^3 + 32*x^2 + 9*x + 80, x^93 + 74*x^91 + 8*x^90 + 35*x^89 + 40*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 24*x^82 + 107*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 93*x^73 + 56*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 8*x^66 + 93*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 47*x^25 + 72*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 120*x^18 + 55*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 89*x^9 + 88*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 104*x^2 + 57*x + 72, x^93 + 74*x^91 + 92*x^90 + 91*x^89 + 92*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 116*x^82 + 51*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 5*x^73 + 116*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 124*x^66 + 53*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 71*x^25 + 12*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 4*x^18 + 31*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 97*x^9 + 36*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 12*x^2 + 49*x + 108, x^93 + 74*x^91 + 12*x^90 + 11*x^89 + 124*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 4*x^82 + 3*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 21*x^73 + 84*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 44*x^66 + 37*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 55*x^25 + 44*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 84*x^18 + 47*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 49*x^9 + 4*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 124*x^2 + 97*x + 12, x^93 + 74*x^91 + 76*x^90 + 27*x^89 + 76*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 68*x^82 + 115*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 69*x^73 + 68*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 108*x^66 + 117*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 7*x^25 + 60*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 20*x^18 + 95*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 33*x^9 + 52*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 60*x^2 + 113*x + 28, x^93 + 74*x^91 + 56*x^90 + 19*x^89 + 72*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 104*x^82 + 59*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 45*x^73 + 24*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 120*x^66 + 77*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 95*x^25 + 104*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 8*x^18 + 71*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 105*x^9 + 56*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 24*x^2 + 105*x + 40, x^93 + 74*x^91 + 64*x^90 + 67*x^89 + 64*x^88 + 4*x^87 + x^85 + 38*x^83 + 64*x^82 + 75*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 61*x^73 + 64*x^72 + 52*x^71 + 7*x^69 + 50*x^67 + 64*x^66 + 125*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 79*x^25 + 64*x^24 + 52*x^23 + 37*x^21 + 94*x^19 + 64*x^18 + 23*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 57*x^9 + 64*x^8 + 4*x^7 + 27*x^5 + 42*x^3 + 64*x^2 + 89*x + 64, x^93 + 74*x^91 + 64*x^90 + 99*x^89 + 32*x^88 + 68*x^87 + 64*x^86 + x^85 + 102*x^83 + 107*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 29*x^73 + 96*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 114*x^67 + 93*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 111*x^25 + 32*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 30*x^19 + 55*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 25*x^9 + 96*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 106*x^3 + 57*x + 96, x^93 + 74*x^91 + 116*x^90 + 123*x^89 + 84*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 60*x^82 + 83*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 101*x^73 + 28*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 20*x^66 + 21*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 103*x^25 + 100*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 108*x^18 + 63*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 65*x^9 + 44*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 68*x^2 + 17*x + 68, x^93 + 74*x^91 + 64*x^90 + 3*x^89 + 32*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 102*x^83 + 75*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 125*x^73 + 96*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 114*x^67 + 125*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 15*x^25 + 32*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 30*x^19 + 23*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 121*x^9 + 96*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 106*x^3 + 89*x + 96, x^93 + 74*x^91 + 36*x^90 + 11*x^89 + 84*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 12*x^82 + 3*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 21*x^73 + 28*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 4*x^66 + 37*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 55*x^25 + 100*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 124*x^18 + 47*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 49*x^9 + 44*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 116*x^2 + 97*x + 4, x^93 + 74*x^91 + 40*x^90 + 51*x^89 + 24*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 56*x^82 + 27*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 13*x^73 + 8*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 104*x^66 + 109*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 127*x^25 + 120*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 24*x^18 + 39*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 73*x^9 + 104*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 72*x^2 + 9*x + 56, x^93 + 74*x^91 + 76*x^90 + 107*x^89 + 124*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 4*x^82 + 99*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 53*x^73 + 84*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 44*x^66 + 69*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 23*x^25 + 44*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 84*x^18 + 15*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 81*x^9 + 4*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 124*x^2 + x + 76, x^93 + 74*x^91 + 112*x^90 + 3*x^89 + 48*x^88 + 4*x^87 + 32*x^86 + x^85 + 32*x^84 + 38*x^83 + 80*x^82 + 11*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 125*x^73 + 16*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 112*x^66 + 61*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 15*x^25 + 112*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 16*x^18 + 87*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 121*x^9 + 80*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 48*x^2 + 25*x + 112, x^93 + 74*x^91 + 68*x^90 + 91*x^89 + 36*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 108*x^82 + 51*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 5*x^73 + 12*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 36*x^66 + 53*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 71*x^25 + 116*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 92*x^18 + 31*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 97*x^9 + 92*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 20*x^2 + 49*x + 20, x^93 + 74*x^91 + 48*x^90 + 99*x^89 + 112*x^88 + 68*x^87 + 96*x^86 + x^85 + 96*x^84 + 102*x^83 + 80*x^82 + 107*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 29*x^73 + 80*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 112*x^66 + 93*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 111*x^25 + 48*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 16*x^18 + 55*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 25*x^9 + 16*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 48*x^2 + 57*x + 112, x^93 + 74*x^91 + 36*x^90 + 27*x^89 + 100*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 76*x^82 + 51*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 69*x^73 + 76*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 68*x^66 + 53*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 7*x^25 + 52*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 60*x^18 + 31*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 33*x^9 + 28*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 52*x^2 + 49*x + 20, x^93 + 74*x^91 + 56*x^90 + 51*x^89 + 104*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 104*x^82 + 27*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 13*x^73 + 120*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 120*x^66 + 109*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 127*x^25 + 8*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 8*x^18 + 39*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 73*x^9 + 24*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 24*x^2 + 9*x + 72, x^93 + 74*x^91 + 44*x^90 + 43*x^89 + 60*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 36*x^82 + 35*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 117*x^73 + 20*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 12*x^66 + 5*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 87*x^25 + 108*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 116*x^18 + 79*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 17*x^9 + 68*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 92*x^2 + 65*x + 12, x^93 + 74*x^91 + 60*x^90 + 75*x^89 + 108*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 84*x^82 + 3*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 85*x^73 + 36*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 28*x^66 + 37*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 119*x^25 + 92*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 100*x^18 + 47*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 113*x^9 + 20*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 44*x^2 + 97*x + 124, x^93 + 74*x^91 + 80*x^90 + 35*x^89 + 16*x^88 + 68*x^87 + 32*x^86 + x^85 + 32*x^84 + 102*x^83 + 48*x^82 + 43*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 93*x^73 + 48*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 16*x^66 + 29*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 47*x^25 + 80*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 112*x^18 + 119*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 89*x^9 + 112*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 80*x^2 + 121*x + 16, x^93 + 74*x^91 + 108*x^90 + 91*x^89 + 108*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 36*x^82 + 51*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 5*x^73 + 36*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 12*x^66 + 53*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 71*x^25 + 92*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 116*x^18 + 31*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 97*x^9 + 20*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 92*x^2 + 49*x + 60, x^93 + 74*x^91 + 88*x^90 + 35*x^89 + 88*x^88 + 68*x^87 + 16*x^86 + x^85 + 80*x^84 + 102*x^83 + 72*x^82 + 43*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 93*x^73 + 72*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 24*x^66 + 29*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 47*x^25 + 56*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 104*x^18 + 119*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 89*x^9 + 40*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 56*x^2 + 121*x + 120, x^93 + 74*x^91 + 64*x^90 + 67*x^89 + 68*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 102*x^83 + 11*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 61*x^73 + 116*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 114*x^67 + 61*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 79*x^25 + 116*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 30*x^19 + 87*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 57*x^9 + 68*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 106*x^3 + 25*x + 64, x^93 + 74*x^91 + 32*x^90 + 99*x^89 + 64*x^88 + 68*x^87 + x^85 + 64*x^84 + 102*x^83 + 32*x^82 + 107*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 29*x^73 + 64*x^72 + 116*x^71 + 7*x^69 + 64*x^68 + 114*x^67 + 96*x^66 + 93*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 111*x^25 + 64*x^24 + 116*x^23 + 37*x^21 + 64*x^20 + 30*x^19 + 32*x^18 + 55*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 25*x^9 + 64*x^8 + 68*x^7 + 27*x^5 + 64*x^4 + 106*x^3 + 96*x^2 + 57*x, x^93 + 74*x^91 + 36*x^90 + 107*x^89 + 20*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 76*x^82 + 99*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 53*x^73 + 92*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 68*x^66 + 69*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 23*x^25 + 36*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 60*x^18 + 15*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 81*x^9 + 108*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 52*x^2 + x + 4, x^93 + 74*x^91 + 8*x^90 + 115*x^89 + 56*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 88*x^82 + 91*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 77*x^73 + 104*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 72*x^66 + 45*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 63*x^25 + 24*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 56*x^18 + 103*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 9*x^9 + 72*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 40*x^2 + 73*x + 88, x^93 + 74*x^91 + 100*x^90 + 123*x^89 + 100*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 12*x^82 + 83*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 101*x^73 + 76*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 4*x^66 + 21*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 103*x^25 + 52*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 124*x^18 + 63*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 65*x^9 + 28*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 116*x^2 + 17*x + 20, x^93 + 74*x^91 + 76*x^90 + 75*x^89 + 28*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 68*x^82 + 67*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 85*x^73 + 52*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 108*x^66 + 101*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 119*x^25 + 76*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 20*x^18 + 111*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 113*x^9 + 100*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 60*x^2 + 33*x + 44, x^93 + 74*x^91 + 120*x^90 + 67*x^89 + 88*x^88 + 4*x^87 + 16*x^86 + x^85 + 16*x^84 + 38*x^83 + 104*x^82 + 75*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 61*x^73 + 72*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 120*x^66 + 125*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 79*x^25 + 56*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 8*x^18 + 23*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 57*x^9 + 40*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 24*x^2 + 89*x + 56, x^93 + 74*x^91 + 40*x^90 + 115*x^89 + 88*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 120*x^82 + 27*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 77*x^73 + 72*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 40*x^66 + 109*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 63*x^25 + 56*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 88*x^18 + 39*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 9*x^9 + 40*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 8*x^2 + 9*x + 56, x^93 + 74*x^91 + 80*x^90 + 115*x^89 + 64*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 102*x^83 + 112*x^82 + 27*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 77*x^73 + 64*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 114*x^67 + 80*x^66 + 109*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 63*x^25 + 64*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 30*x^19 + 48*x^18 + 39*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 9*x^9 + 64*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 106*x^3 + 16*x^2 + 9*x + 64, x^93 + 74*x^91 + 67*x^89 + 68*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 102*x^83 + 64*x^82 + 11*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 61*x^73 + 116*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 114*x^67 + 64*x^66 + 61*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 79*x^25 + 116*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 30*x^19 + 64*x^18 + 87*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 57*x^9 + 68*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 106*x^3 + 64*x^2 + 25*x + 64, x^93 + 74*x^91 + 68*x^90 + 123*x^89 + 4*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 44*x^82 + 83*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 101*x^73 + 44*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 100*x^66 + 21*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 103*x^25 + 84*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 28*x^18 + 63*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 65*x^9 + 124*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 84*x^2 + 17*x + 52, x^93 + 74*x^91 + 96*x^90 + 19*x^89 + 48*x^88 + 4*x^87 + 97*x^85 + 96*x^84 + 38*x^83 + 96*x^82 + 59*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 45*x^73 + 16*x^72 + 52*x^71 + 103*x^69 + 96*x^68 + 50*x^67 + 32*x^66 + 77*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 95*x^25 + 112*x^24 + 52*x^23 + 5*x^21 + 96*x^20 + 94*x^19 + 96*x^18 + 71*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 105*x^9 + 80*x^8 + 4*x^7 + 123*x^5 + 96*x^4 + 42*x^3 + 32*x^2 + 105*x + 48, x^93 + 74*x^91 + 32*x^90 + 51*x^89 + 16*x^88 + 4*x^87 + 33*x^85 + 32*x^84 + 38*x^83 + 32*x^82 + 27*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 13*x^73 + 48*x^72 + 52*x^71 + 39*x^69 + 32*x^68 + 50*x^67 + 96*x^66 + 109*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 127*x^25 + 80*x^24 + 52*x^23 + 69*x^21 + 32*x^20 + 94*x^19 + 32*x^18 + 39*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 73*x^9 + 112*x^8 + 4*x^7 + 59*x^5 + 32*x^4 + 42*x^3 + 96*x^2 + 9*x + 16, x^93 + 74*x^91 + 60*x^90 + 59*x^89 + 92*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 84*x^82 + 19*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 37*x^73 + 116*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 28*x^66 + 85*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 39*x^25 + 12*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 100*x^18 + 127*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + x^9 + 36*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 44*x^2 + 81*x + 44, x^93 + 74*x^91 + 72*x^90 + 67*x^89 + 40*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 24*x^82 + 11*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 61*x^73 + 56*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 8*x^66 + 61*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 79*x^25 + 72*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 120*x^18 + 87*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 57*x^9 + 88*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 104*x^2 + 25*x + 8, x^93 + 74*x^91 + 80*x^90 + 115*x^89 + 32*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 112*x^82 + 27*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 77*x^73 + 96*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 80*x^66 + 109*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 63*x^25 + 32*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 48*x^18 + 39*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 9*x^9 + 96*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 16*x^2 + 9*x + 32, x^93 + 74*x^91 + 48*x^90 + 67*x^89 + 112*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 80*x^82 + 11*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 61*x^73 + 80*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 112*x^66 + 61*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 79*x^25 + 48*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 16*x^18 + 87*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 57*x^9 + 16*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 48*x^2 + 25*x + 112, x^93 + 74*x^91 + 108*x^90 + 59*x^89 + 76*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 100*x^82 + 19*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 37*x^73 + 68*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 76*x^66 + 85*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 39*x^25 + 60*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 52*x^18 + 127*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + x^9 + 52*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 28*x^2 + 81*x + 92, x^93 + 74*x^91 + 112*x^90 + 19*x^89 + 64*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 102*x^83 + 80*x^82 + 123*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 45*x^73 + 64*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 114*x^67 + 112*x^66 + 13*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 95*x^25 + 64*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 30*x^19 + 16*x^18 + 7*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 105*x^9 + 64*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 106*x^3 + 48*x^2 + 41*x + 64, x^93 + 74*x^91 + 16*x^90 + 115*x^89 + 4*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 112*x^82 + 91*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 77*x^73 + 52*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 80*x^66 + 45*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 63*x^25 + 52*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 48*x^18 + 103*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 9*x^9 + 4*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 16*x^2 + 73*x + 64, x^93 + 74*x^91 + 20*x^90 + 27*x^89 + 84*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 28*x^82 + 51*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 69*x^73 + 28*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 52*x^66 + 53*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 7*x^25 + 100*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 76*x^18 + 31*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 33*x^9 + 44*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 100*x^2 + 49*x + 68, x^93 + 74*x^91 + 36*x^90 + 27*x^89 + 4*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 12*x^82 + 115*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 69*x^73 + 44*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 4*x^66 + 117*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 7*x^25 + 84*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 124*x^18 + 95*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 33*x^9 + 124*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 116*x^2 + 113*x + 116, x^93 + 74*x^91 + 40*x^90 + 51*x^89 + 120*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 120*x^82 + 91*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 13*x^73 + 40*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 40*x^66 + 45*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 127*x^25 + 88*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 88*x^18 + 103*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 73*x^9 + 8*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 8*x^2 + 73*x + 88, x^93 + 74*x^91 + 104*x^90 + 19*x^89 + 24*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 120*x^82 + 59*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 45*x^73 + 8*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 40*x^66 + 77*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 95*x^25 + 120*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 88*x^18 + 71*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 105*x^9 + 104*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 8*x^2 + 105*x + 56, x^93 + 74*x^91 + 100*x^90 + 107*x^89 + 52*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 12*x^82 + 99*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 53*x^73 + 60*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 4*x^66 + 69*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 23*x^25 + 68*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 124*x^18 + 15*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 81*x^9 + 76*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 116*x^2 + x + 36, x^93 + 74*x^91 + 24*x^90 + 99*x^89 + 88*x^88 + 68*x^87 + 16*x^86 + x^85 + 80*x^84 + 102*x^83 + 8*x^82 + 107*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 29*x^73 + 72*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 88*x^66 + 93*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 111*x^25 + 56*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 40*x^18 + 55*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 25*x^9 + 40*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 120*x^2 + 57*x + 120, x^93 + 74*x^91 + 124*x^90 + 123*x^89 + 92*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 84*x^82 + 19*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 101*x^73 + 116*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 28*x^66 + 85*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 103*x^25 + 12*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 100*x^18 + 127*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 65*x^9 + 36*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 44*x^2 + 81*x + 108, x^93 + 74*x^91 + 80*x^90 + 99*x^89 + 80*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 112*x^82 + 43*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 29*x^73 + 112*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 80*x^66 + 29*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 111*x^25 + 16*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 48*x^18 + 119*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 25*x^9 + 48*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 16*x^2 + 121*x + 16, x^93 + 74*x^91 + 120*x^90 + 99*x^89 + 56*x^88 + 68*x^87 + 80*x^86 + x^85 + 16*x^84 + 102*x^83 + 40*x^82 + 107*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 29*x^73 + 104*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 56*x^66 + 93*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 111*x^25 + 24*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 72*x^18 + 55*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 25*x^9 + 72*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 88*x^2 + 57*x + 88, x^93 + 74*x^91 + 72*x^90 + 19*x^89 + 88*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 24*x^82 + 59*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 45*x^73 + 72*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 8*x^66 + 77*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 95*x^25 + 56*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 120*x^18 + 71*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 105*x^9 + 40*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 104*x^2 + 105*x + 120, x^93 + 74*x^91 + 84*x^90 + 107*x^89 + 4*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 92*x^82 + 99*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 53*x^73 + 44*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 116*x^66 + 69*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 23*x^25 + 84*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 12*x^18 + 15*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 81*x^9 + 124*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 36*x^2 + x + 52, x^93 + 74*x^91 + 120*x^90 + 115*x^89 + 104*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 40*x^82 + 91*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 77*x^73 + 120*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 56*x^66 + 45*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 63*x^25 + 8*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 72*x^18 + 103*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 9*x^9 + 24*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 88*x^2 + 73*x + 72, x^93 + 74*x^91 + 120*x^90 + 115*x^89 + 104*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 104*x^82 + 27*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 77*x^73 + 120*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 120*x^66 + 109*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 63*x^25 + 8*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 8*x^18 + 39*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 9*x^9 + 24*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 24*x^2 + 9*x + 8, x^93 + 74*x^91 + 28*x^90 + 75*x^89 + 76*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 116*x^82 + 3*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 85*x^73 + 68*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 124*x^66 + 37*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 119*x^25 + 60*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 4*x^18 + 47*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 113*x^9 + 52*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 12*x^2 + 97*x + 92, x^93 + 74*x^91 + 64*x^90 + 99*x^89 + 4*x^87 + 65*x^85 + 38*x^83 + 64*x^82 + 43*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 29*x^73 + 52*x^71 + 71*x^69 + 50*x^67 + 64*x^66 + 29*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 111*x^25 + 52*x^23 + 101*x^21 + 94*x^19 + 64*x^18 + 119*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 25*x^9 + 4*x^7 + 91*x^5 + 42*x^3 + 64*x^2 + 121*x, x^93 + 74*x^91 + 12*x^90 + 59*x^89 + 44*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 68*x^82 + 19*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 37*x^73 + 100*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 108*x^66 + 85*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 39*x^25 + 28*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 20*x^18 + 127*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + x^9 + 84*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 60*x^2 + 81*x + 60, x^93 + 74*x^91 + 16*x^90 + 51*x^89 + 4*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 112*x^82 + 27*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 13*x^73 + 52*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 80*x^66 + 109*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 127*x^25 + 52*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 48*x^18 + 39*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 73*x^9 + 4*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 16*x^2 + 9*x + 64, x^93 + 74*x^91 + 52*x^90 + 123*x^89 + 116*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 124*x^82 + 83*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 101*x^73 + 124*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 84*x^66 + 21*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 103*x^25 + 4*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 44*x^18 + 63*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 65*x^9 + 12*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 4*x^2 + 17*x + 100, x^93 + 74*x^91 + 124*x^90 + 43*x^89 + 76*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 20*x^82 + 35*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 117*x^73 + 68*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 92*x^66 + 5*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 87*x^25 + 60*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 36*x^18 + 79*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 17*x^9 + 52*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 108*x^2 + 65*x + 92, x^93 + 74*x^91 + 24*x^90 + 3*x^89 + 88*x^88 + 4*x^87 + 80*x^86 + x^85 + 16*x^84 + 38*x^83 + 72*x^82 + 11*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 125*x^73 + 72*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 24*x^66 + 61*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 15*x^25 + 56*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 104*x^18 + 87*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 121*x^9 + 40*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 56*x^2 + 25*x + 56, x^93 + 74*x^91 + 60*x^90 + 59*x^89 + 28*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 20*x^82 + 83*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 37*x^73 + 52*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 92*x^66 + 21*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 39*x^25 + 76*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 36*x^18 + 63*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + x^9 + 100*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 108*x^2 + 17*x + 44, x^93 + 74*x^91 + 20*x^90 + 107*x^89 + 36*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 92*x^82 + 35*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 53*x^73 + 12*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 116*x^66 + 5*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 23*x^25 + 116*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 12*x^18 + 79*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 81*x^9 + 92*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 36*x^2 + 65*x + 20, x^93 + 74*x^91 + 112*x^90 + 115*x^89 + 96*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 80*x^82 + 27*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 77*x^73 + 32*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 112*x^66 + 109*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 63*x^25 + 96*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 16*x^18 + 39*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 9*x^9 + 32*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 48*x^2 + 9*x + 96, x^93 + 74*x^91 + 96*x^90 + 3*x^89 + 4*x^87 + 64*x^86 + x^85 + 38*x^83 + 32*x^82 + 11*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 125*x^73 + 52*x^71 + 64*x^70 + 7*x^69 + 50*x^67 + 96*x^66 + 61*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 15*x^25 + 52*x^23 + 64*x^22 + 37*x^21 + 94*x^19 + 32*x^18 + 87*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 121*x^9 + 4*x^7 + 64*x^6 + 27*x^5 + 42*x^3 + 96*x^2 + 25*x, x^93 + 74*x^91 + 36*x^90 + 59*x^89 + 68*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 12*x^82 + 83*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 37*x^73 + 108*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 4*x^66 + 21*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 39*x^25 + 20*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 124*x^18 + 63*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + x^9 + 60*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 116*x^2 + 17*x + 52, x^93 + 74*x^91 + 120*x^90 + 67*x^89 + 120*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 40*x^82 + 11*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 61*x^73 + 40*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 56*x^66 + 61*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 79*x^25 + 88*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 72*x^18 + 87*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 57*x^9 + 8*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 88*x^2 + 25*x + 24, x^93 + 74*x^91 + 4*x^90 + 123*x^89 + 68*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 44*x^82 + 19*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 101*x^73 + 108*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 100*x^66 + 85*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 103*x^25 + 20*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 28*x^18 + 127*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 65*x^9 + 60*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 84*x^2 + 81*x + 52, x^93 + 74*x^91 + 32*x^90 + 83*x^89 + 80*x^88 + 4*x^87 + 97*x^85 + 32*x^84 + 38*x^83 + 32*x^82 + 123*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 109*x^73 + 112*x^72 + 52*x^71 + 103*x^69 + 32*x^68 + 50*x^67 + 96*x^66 + 13*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 31*x^25 + 16*x^24 + 52*x^23 + 5*x^21 + 32*x^20 + 94*x^19 + 32*x^18 + 7*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 41*x^9 + 48*x^8 + 4*x^7 + 123*x^5 + 32*x^4 + 42*x^3 + 96*x^2 + 41*x + 80, x^93 + 74*x^91 + 104*x^90 + 35*x^89 + 40*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 56*x^82 + 107*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 93*x^73 + 56*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 104*x^66 + 93*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 47*x^25 + 72*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 24*x^18 + 55*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 89*x^9 + 88*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 72*x^2 + 57*x + 72, x^93 + 74*x^91 + 108*x^90 + 107*x^89 + 124*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 100*x^82 + 99*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 53*x^73 + 84*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 76*x^66 + 69*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 23*x^25 + 44*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 52*x^18 + 15*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 81*x^9 + 4*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 28*x^2 + x + 76, x^93 + 74*x^91 + 48*x^90 + 67*x^89 + 48*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 80*x^82 + 11*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 61*x^73 + 16*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 112*x^66 + 61*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 79*x^25 + 112*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 16*x^18 + 87*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 57*x^9 + 80*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 48*x^2 + 25*x + 48, x^93 + 74*x^91 + 51*x^89 + 16*x^88 + 68*x^87 + 97*x^85 + 96*x^84 + 102*x^83 + 91*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 13*x^73 + 48*x^72 + 116*x^71 + 103*x^69 + 96*x^68 + 114*x^67 + 45*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 127*x^25 + 80*x^24 + 116*x^23 + 5*x^21 + 96*x^20 + 30*x^19 + 103*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 73*x^9 + 112*x^8 + 68*x^7 + 123*x^5 + 96*x^4 + 106*x^3 + 73*x + 80, x^93 + 74*x^91 + 104*x^90 + 83*x^89 + 24*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 56*x^82 + 59*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 109*x^73 + 8*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 104*x^66 + 77*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 31*x^25 + 120*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 24*x^18 + 71*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 41*x^9 + 104*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 72*x^2 + 105*x + 120, x^93 + 74*x^91 + 24*x^90 + 83*x^89 + 72*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 72*x^82 + 59*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 109*x^73 + 24*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 24*x^66 + 77*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 31*x^25 + 104*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 104*x^18 + 71*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 41*x^9 + 56*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 56*x^2 + 105*x + 104, x^93 + 74*x^91 + 68*x^90 + 107*x^89 + 52*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 108*x^82 + 35*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 53*x^73 + 60*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 36*x^66 + 5*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 23*x^25 + 68*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 92*x^18 + 79*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 81*x^9 + 76*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 20*x^2 + 65*x + 100, x^93 + 74*x^91 + 88*x^90 + 99*x^89 + 56*x^88 + 68*x^87 + 16*x^86 + x^85 + 16*x^84 + 102*x^83 + 72*x^82 + 107*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 29*x^73 + 104*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 24*x^66 + 93*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 111*x^25 + 24*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 104*x^18 + 55*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 25*x^9 + 72*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 56*x^2 + 57*x + 88, x^93 + 74*x^91 + 116*x^90 + 91*x^89 + 116*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 60*x^82 + 115*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 5*x^73 + 124*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 20*x^66 + 117*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 71*x^25 + 4*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 108*x^18 + 95*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 97*x^9 + 12*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 68*x^2 + 113*x + 100, x^93 + 74*x^91 + 60*x^90 + 91*x^89 + 28*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 84*x^82 + 115*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 5*x^73 + 52*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 28*x^66 + 117*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 71*x^25 + 76*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 100*x^18 + 95*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 97*x^9 + 100*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 44*x^2 + 113*x + 108, x^93 + 74*x^91 + 80*x^90 + 67*x^89 + 112*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 48*x^82 + 11*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 61*x^73 + 80*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 16*x^66 + 61*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 79*x^25 + 48*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 112*x^18 + 87*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 57*x^9 + 16*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 80*x^2 + 25*x + 112, x^93 + 74*x^91 + 28*x^90 + 11*x^89 + 76*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 52*x^82 + 3*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 21*x^73 + 68*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 60*x^66 + 37*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 55*x^25 + 60*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 68*x^18 + 47*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 49*x^9 + 52*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 76*x^2 + 97*x + 28, x^93 + 74*x^91 + 52*x^90 + 75*x^89 + 68*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 60*x^82 + 67*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 85*x^73 + 108*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 20*x^66 + 101*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 119*x^25 + 20*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 108*x^18 + 111*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 113*x^9 + 60*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 68*x^2 + 33*x + 52, x^93 + 74*x^91 + 112*x^90 + 115*x^89 + 32*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 80*x^82 + 27*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 77*x^73 + 96*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 112*x^66 + 109*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 63*x^25 + 32*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 16*x^18 + 39*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 9*x^9 + 96*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 48*x^2 + 9*x + 32, x^93 + 74*x^91 + 24*x^90 + 115*x^89 + 40*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 72*x^82 + 27*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 77*x^73 + 56*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 24*x^66 + 109*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 63*x^25 + 72*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 104*x^18 + 39*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 9*x^9 + 88*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 56*x^2 + 9*x + 72, x^93 + 74*x^91 + 80*x^90 + 35*x^89 + 16*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 112*x^82 + 107*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 93*x^73 + 48*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 80*x^66 + 93*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 47*x^25 + 80*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 48*x^18 + 55*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 89*x^9 + 112*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 16*x^2 + 57*x + 80, x^93 + 74*x^91 + 68*x^90 + 107*x^89 + 20*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 108*x^82 + 35*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 53*x^73 + 92*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 36*x^66 + 5*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 23*x^25 + 36*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 92*x^18 + 79*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 81*x^9 + 108*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 20*x^2 + 65*x + 68, x^93 + 74*x^91 + 76*x^90 + 27*x^89 + 44*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 68*x^82 + 115*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 69*x^73 + 100*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 108*x^66 + 117*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 7*x^25 + 28*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 20*x^18 + 95*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 33*x^9 + 84*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 60*x^2 + 113*x + 124, x^93 + 74*x^91 + 60*x^90 + 11*x^89 + 44*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 84*x^82 + 67*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 21*x^73 + 100*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 28*x^66 + 101*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 55*x^25 + 28*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 100*x^18 + 111*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 49*x^9 + 84*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 44*x^2 + 33*x + 60, x^93 + 74*x^91 + 88*x^90 + 67*x^89 + 24*x^88 + 4*x^87 + 80*x^86 + x^85 + 16*x^84 + 38*x^83 + 8*x^82 + 75*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 61*x^73 + 8*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 88*x^66 + 125*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 79*x^25 + 120*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 40*x^18 + 23*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 57*x^9 + 104*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 120*x^2 + 89*x + 120, x^93 + 74*x^91 + 116*x^90 + 59*x^89 + 116*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 124*x^82 + 83*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 37*x^73 + 124*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 84*x^66 + 21*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 39*x^25 + 4*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 44*x^18 + 63*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + x^9 + 12*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 4*x^2 + 17*x + 36, x^93 + 74*x^91 + 120*x^90 + 35*x^89 + 88*x^88 + 68*x^87 + 80*x^86 + x^85 + 80*x^84 + 102*x^83 + 40*x^82 + 43*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 93*x^73 + 72*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 56*x^66 + 29*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 47*x^25 + 56*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 72*x^18 + 119*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 89*x^9 + 40*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 88*x^2 + 121*x + 120, x^93 + 74*x^91 + 68*x^90 + 59*x^89 + 36*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 44*x^82 + 19*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 37*x^73 + 12*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 100*x^66 + 85*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 39*x^25 + 116*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 28*x^18 + 127*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + x^9 + 92*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 84*x^2 + 81*x + 84, x^93 + 74*x^91 + 8*x^90 + 67*x^89 + 8*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 88*x^82 + 11*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 61*x^73 + 88*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 72*x^66 + 61*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 79*x^25 + 40*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 56*x^18 + 87*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 57*x^9 + 120*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 40*x^2 + 25*x + 104, x^93 + 74*x^91 + 76*x^90 + 107*x^89 + 92*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 68*x^82 + 35*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 53*x^73 + 116*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 108*x^66 + 5*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 23*x^25 + 12*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 20*x^18 + 79*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 81*x^9 + 36*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 60*x^2 + 65*x + 108, x^93 + 74*x^91 + 80*x^90 + 3*x^89 + 80*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 48*x^82 + 75*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 125*x^73 + 112*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 16*x^66 + 125*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 15*x^25 + 16*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 112*x^18 + 23*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 121*x^9 + 48*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 80*x^2 + 89*x + 80, x^93 + 74*x^91 + 8*x^90 + 83*x^89 + 88*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 88*x^82 + 123*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 109*x^73 + 72*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 72*x^66 + 13*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 31*x^25 + 56*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 56*x^18 + 7*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 41*x^9 + 40*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 40*x^2 + 41*x + 120, x^93 + 74*x^91 + 96*x^90 + 51*x^89 + 112*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 102*x^83 + 32*x^82 + 91*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 13*x^73 + 80*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 114*x^67 + 96*x^66 + 45*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 127*x^25 + 48*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 30*x^19 + 32*x^18 + 103*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 73*x^9 + 16*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 106*x^3 + 96*x^2 + 73*x + 48, x^93 + 74*x^91 + 76*x^90 + 43*x^89 + 92*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 4*x^82 + 35*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 117*x^73 + 116*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 44*x^66 + 5*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 87*x^25 + 12*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 84*x^18 + 79*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 17*x^9 + 36*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 124*x^2 + 65*x + 44, x^93 + 74*x^91 + 96*x^90 + 3*x^89 + 32*x^88 + 4*x^87 + 64*x^86 + x^85 + 64*x^84 + 38*x^83 + 32*x^82 + 11*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 125*x^73 + 96*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 50*x^67 + 96*x^66 + 61*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 15*x^25 + 32*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 94*x^19 + 32*x^18 + 87*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 121*x^9 + 96*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 42*x^3 + 96*x^2 + 25*x + 32, x^93 + 74*x^91 + 52*x^90 + 11*x^89 + 36*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 60*x^82 + 3*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 21*x^73 + 12*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 20*x^66 + 37*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 55*x^25 + 116*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 108*x^18 + 47*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 49*x^9 + 92*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 68*x^2 + 97*x + 20, x^93 + 74*x^91 + 104*x^90 + 67*x^89 + 104*x^88 + 4*x^87 + 48*x^86 + x^85 + 112*x^84 + 38*x^83 + 56*x^82 + 75*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 61*x^73 + 120*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 104*x^66 + 125*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 79*x^25 + 8*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 24*x^18 + 23*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 57*x^9 + 24*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 72*x^2 + 89*x + 8, x^93 + 74*x^91 + 76*x^90 + 107*x^89 + 28*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 68*x^82 + 35*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 53*x^73 + 52*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 108*x^66 + 5*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 23*x^25 + 76*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 20*x^18 + 79*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 81*x^9 + 100*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 60*x^2 + 65*x + 44, x^93 + 74*x^91 + 104*x^90 + 99*x^89 + 40*x^88 + 68*x^87 + 112*x^86 + x^85 + 48*x^84 + 102*x^83 + 120*x^82 + 107*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 29*x^73 + 56*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 40*x^66 + 93*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 111*x^25 + 72*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 88*x^18 + 55*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 25*x^9 + 88*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 8*x^2 + 57*x + 8, x^93 + 74*x^91 + 108*x^90 + 123*x^89 + 12*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 36*x^82 + 19*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 101*x^73 + 4*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 12*x^66 + 85*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 103*x^25 + 124*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 116*x^18 + 127*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 65*x^9 + 116*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 92*x^2 + 81*x + 92, x^93 + 74*x^91 + 76*x^90 + 59*x^89 + 44*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 68*x^82 + 83*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 37*x^73 + 100*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 108*x^66 + 21*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 39*x^25 + 28*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 20*x^18 + 63*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + x^9 + 84*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 60*x^2 + 17*x + 124, x^93 + 74*x^91 + 48*x^90 + 115*x^89 + 96*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 38*x^83 + 80*x^82 + 91*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 77*x^73 + 32*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 50*x^67 + 112*x^66 + 45*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 63*x^25 + 96*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 94*x^19 + 16*x^18 + 103*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 9*x^9 + 32*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 42*x^3 + 48*x^2 + 73*x + 32, x^93 + 74*x^91 + 8*x^90 + 35*x^89 + 72*x^88 + 68*x^87 + 48*x^86 + x^85 + 112*x^84 + 102*x^83 + 88*x^82 + 43*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 93*x^73 + 24*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 72*x^66 + 29*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 47*x^25 + 104*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 56*x^18 + 119*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 89*x^9 + 56*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 40*x^2 + 121*x + 40, x^93 + 74*x^91 + 68*x^90 + 11*x^89 + 116*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 108*x^82 + 3*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 21*x^73 + 124*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 36*x^66 + 37*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 55*x^25 + 4*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 92*x^18 + 47*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 49*x^9 + 12*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 20*x^2 + 97*x + 36, x^93 + 74*x^91 + 48*x^90 + 115*x^89 + 4*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 80*x^82 + 91*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 77*x^73 + 52*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 112*x^66 + 45*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 63*x^25 + 52*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 16*x^18 + 103*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 9*x^9 + 4*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 48*x^2 + 73*x + 64, x^93 + 74*x^91 + 40*x^90 + 115*x^89 + 88*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 56*x^82 + 91*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 77*x^73 + 72*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 104*x^66 + 45*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 63*x^25 + 56*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 24*x^18 + 103*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 9*x^9 + 40*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 72*x^2 + 73*x + 120, x^93 + 74*x^91 + 36*x^90 + 11*x^89 + 52*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 12*x^82 + 3*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 21*x^73 + 60*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 4*x^66 + 37*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 55*x^25 + 68*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 124*x^18 + 47*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 49*x^9 + 76*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 116*x^2 + 97*x + 100, x^93 + 74*x^91 + 24*x^90 + 3*x^89 + 88*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 8*x^82 + 75*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 125*x^73 + 72*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 88*x^66 + 125*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 15*x^25 + 56*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 40*x^18 + 23*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 121*x^9 + 40*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 120*x^2 + 89*x + 120, x^93 + 74*x^91 + 44*x^90 + 75*x^89 + 60*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 100*x^82 + 67*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 85*x^73 + 20*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 76*x^66 + 101*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 119*x^25 + 108*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 52*x^18 + 111*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 113*x^9 + 68*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 28*x^2 + 33*x + 76, x^93 + 74*x^91 + 48*x^90 + 3*x^89 + 80*x^88 + 4*x^87 + 32*x^86 + x^85 + 96*x^84 + 38*x^83 + 16*x^82 + 11*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 125*x^73 + 112*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 48*x^66 + 61*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 15*x^25 + 16*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 80*x^18 + 87*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 121*x^9 + 48*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 112*x^2 + 25*x + 16, x^93 + 74*x^91 + 84*x^90 + 107*x^89 + 4*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 28*x^82 + 35*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 53*x^73 + 44*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 52*x^66 + 5*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 23*x^25 + 84*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 76*x^18 + 79*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 81*x^9 + 124*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 100*x^2 + 65*x + 116, x^93 + 74*x^91 + 40*x^90 + 115*x^89 + 24*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 56*x^82 + 91*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 77*x^73 + 8*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 104*x^66 + 45*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 63*x^25 + 120*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 24*x^18 + 103*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 9*x^9 + 104*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 72*x^2 + 73*x + 56, x^93 + 74*x^91 + 36*x^90 + 27*x^89 + 100*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 12*x^82 + 115*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 69*x^73 + 76*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 4*x^66 + 117*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 7*x^25 + 52*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 124*x^18 + 95*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 33*x^9 + 28*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 116*x^2 + 113*x + 84, x^93 + 74*x^91 + 32*x^90 + 35*x^89 + 64*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 38*x^83 + 96*x^82 + 107*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 93*x^73 + 64*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 50*x^67 + 32*x^66 + 93*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 47*x^25 + 64*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 94*x^19 + 96*x^18 + 55*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 89*x^9 + 64*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 42*x^3 + 32*x^2 + 57*x + 64, x^93 + 74*x^91 + 56*x^90 + 115*x^89 + 104*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 40*x^82 + 27*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 77*x^73 + 120*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 56*x^66 + 109*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 63*x^25 + 8*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 72*x^18 + 39*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 9*x^9 + 24*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 88*x^2 + 9*x + 8, x^93 + 74*x^91 + 76*x^90 + 59*x^89 + 108*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 68*x^82 + 83*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 37*x^73 + 36*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 108*x^66 + 21*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 39*x^25 + 92*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 20*x^18 + 63*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + x^9 + 20*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 60*x^2 + 17*x + 60, x^93 + 74*x^91 + 80*x^90 + 35*x^89 + 80*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 112*x^82 + 107*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 93*x^73 + 112*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 80*x^66 + 93*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 47*x^25 + 16*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 48*x^18 + 55*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 89*x^9 + 48*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 16*x^2 + 57*x + 16, x^93 + 74*x^91 + 76*x^90 + 123*x^89 + 108*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 4*x^82 + 83*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 101*x^73 + 36*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 44*x^66 + 21*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 103*x^25 + 92*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 84*x^18 + 63*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 65*x^9 + 20*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 124*x^2 + 17*x + 124, x^93 + 74*x^91 + 32*x^90 + 35*x^89 + 32*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 38*x^83 + 96*x^82 + 107*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 93*x^73 + 96*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 50*x^67 + 32*x^66 + 93*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 47*x^25 + 32*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 94*x^19 + 96*x^18 + 55*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 89*x^9 + 96*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 42*x^3 + 32*x^2 + 57*x + 32, x^93 + 74*x^91 + 96*x^90 + 51*x^89 + 16*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 102*x^83 + 32*x^82 + 91*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 13*x^73 + 48*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 114*x^67 + 96*x^66 + 45*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 127*x^25 + 80*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 30*x^19 + 32*x^18 + 103*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 73*x^9 + 112*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 106*x^3 + 96*x^2 + 73*x + 80, x^93 + 74*x^91 + 120*x^90 + 99*x^89 + 120*x^88 + 68*x^87 + 80*x^86 + x^85 + 16*x^84 + 102*x^83 + 40*x^82 + 107*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 29*x^73 + 40*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 56*x^66 + 93*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 111*x^25 + 88*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 72*x^18 + 55*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 25*x^9 + 8*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 88*x^2 + 57*x + 24, x^93 + 74*x^91 + 4*x^90 + 107*x^89 + 84*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 44*x^82 + 35*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 53*x^73 + 28*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 100*x^66 + 5*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 23*x^25 + 100*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 28*x^18 + 79*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 81*x^9 + 44*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 84*x^2 + 65*x + 4, x^93 + 74*x^91 + 3*x^89 + 4*x^87 + x^85 + 38*x^83 + 11*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 125*x^73 + 52*x^71 + 7*x^69 + 50*x^67 + 61*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 15*x^25 + 52*x^23 + 37*x^21 + 94*x^19 + 87*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 121*x^9 + 4*x^7 + 27*x^5 + 42*x^3 + 25*x, x^93 + 74*x^91 + 88*x^90 + 99*x^89 + 24*x^88 + 68*x^87 + 16*x^86 + x^85 + 80*x^84 + 102*x^83 + 72*x^82 + 107*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 29*x^73 + 8*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 24*x^66 + 93*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 111*x^25 + 120*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 104*x^18 + 55*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 25*x^9 + 104*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 56*x^2 + 57*x + 56, x^93 + 74*x^91 + 116*x^90 + 107*x^89 + 100*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 124*x^82 + 35*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 53*x^73 + 76*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 84*x^66 + 5*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 23*x^25 + 52*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 44*x^18 + 79*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 81*x^9 + 28*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 4*x^2 + 65*x + 84, x^93 + 74*x^91 + 12*x^90 + 75*x^89 + 92*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 4*x^82 + 67*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 85*x^73 + 116*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 44*x^66 + 101*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 119*x^25 + 12*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 84*x^18 + 111*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 113*x^9 + 36*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 124*x^2 + 33*x + 108, x^93 + 74*x^91 + 96*x^90 + 83*x^89 + 16*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 102*x^83 + 32*x^82 + 59*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 109*x^73 + 48*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 114*x^67 + 96*x^66 + 77*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 31*x^25 + 80*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 30*x^19 + 32*x^18 + 71*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 41*x^9 + 112*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 106*x^3 + 96*x^2 + 105*x + 80, x^93 + 74*x^91 + 96*x^90 + 3*x^89 + 68*x^87 + 65*x^85 + 64*x^84 + 102*x^83 + 96*x^82 + 75*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 125*x^73 + 116*x^71 + 71*x^69 + 64*x^68 + 114*x^67 + 32*x^66 + 125*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 15*x^25 + 116*x^23 + 101*x^21 + 64*x^20 + 30*x^19 + 96*x^18 + 23*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 121*x^9 + 68*x^7 + 91*x^5 + 64*x^4 + 106*x^3 + 32*x^2 + 89*x + 64, x^93 + 74*x^91 + 104*x^90 + 67*x^89 + 40*x^88 + 4*x^87 + 48*x^86 + x^85 + 112*x^84 + 38*x^83 + 56*x^82 + 75*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 61*x^73 + 56*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 104*x^66 + 125*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 79*x^25 + 72*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 24*x^18 + 23*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 57*x^9 + 88*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 72*x^2 + 89*x + 72, x^93 + 74*x^91 + 92*x^90 + 123*x^89 + 28*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 116*x^82 + 19*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 101*x^73 + 52*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 124*x^66 + 85*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 103*x^25 + 76*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 4*x^18 + 127*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 65*x^9 + 100*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 12*x^2 + 81*x + 44, x^93 + 74*x^91 + 32*x^90 + 35*x^89 + 64*x^88 + 68*x^87 + x^85 + 64*x^84 + 102*x^83 + 32*x^82 + 43*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 93*x^73 + 64*x^72 + 116*x^71 + 7*x^69 + 64*x^68 + 114*x^67 + 96*x^66 + 29*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 47*x^25 + 64*x^24 + 116*x^23 + 37*x^21 + 64*x^20 + 30*x^19 + 32*x^18 + 119*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 89*x^9 + 64*x^8 + 68*x^7 + 27*x^5 + 64*x^4 + 106*x^3 + 96*x^2 + 121*x, x^93 + 74*x^91 + 35*x^89 + 32*x^88 + 4*x^87 + 65*x^85 + 64*x^84 + 38*x^83 + 107*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 93*x^73 + 96*x^72 + 52*x^71 + 71*x^69 + 64*x^68 + 50*x^67 + 93*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 47*x^25 + 32*x^24 + 52*x^23 + 101*x^21 + 64*x^20 + 94*x^19 + 55*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 89*x^9 + 96*x^8 + 4*x^7 + 91*x^5 + 64*x^4 + 42*x^3 + 57*x + 32, x^93 + 74*x^91 + 48*x^90 + 19*x^89 + 96*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 38*x^83 + 80*x^82 + 59*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 45*x^73 + 32*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 50*x^67 + 112*x^66 + 77*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 95*x^25 + 96*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 94*x^19 + 16*x^18 + 71*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 105*x^9 + 32*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 42*x^3 + 48*x^2 + 105*x + 32, x^93 + 74*x^91 + 56*x^90 + 83*x^89 + 8*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 40*x^82 + 59*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 109*x^73 + 88*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 56*x^66 + 77*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 31*x^25 + 40*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 72*x^18 + 71*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 41*x^9 + 120*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 88*x^2 + 105*x + 40, x^93 + 74*x^91 + 36*x^90 + 11*x^89 + 116*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 76*x^82 + 67*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 21*x^73 + 124*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 68*x^66 + 101*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 55*x^25 + 4*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 60*x^18 + 111*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 49*x^9 + 12*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 52*x^2 + 33*x + 100, x^93 + 74*x^91 + 8*x^90 + 19*x^89 + 88*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 88*x^82 + 59*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 45*x^73 + 72*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 72*x^66 + 77*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 95*x^25 + 56*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 56*x^18 + 71*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 105*x^9 + 40*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 40*x^2 + 105*x + 120, x^93 + 74*x^91 + 4*x^90 + 43*x^89 + 20*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 44*x^82 + 99*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 117*x^73 + 92*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 100*x^66 + 69*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 87*x^25 + 36*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 28*x^18 + 15*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 17*x^9 + 108*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 84*x^2 + x + 68, x^93 + 74*x^91 + 60*x^90 + 59*x^89 + 92*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 20*x^82 + 83*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 37*x^73 + 116*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 92*x^66 + 21*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 39*x^25 + 12*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 36*x^18 + 63*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + x^9 + 36*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 108*x^2 + 17*x + 108, x^93 + 74*x^91 + 48*x^90 + 3*x^89 + 112*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 80*x^82 + 75*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 125*x^73 + 80*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 112*x^66 + 125*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 15*x^25 + 48*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 16*x^18 + 23*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 121*x^9 + 16*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 48*x^2 + 89*x + 112, x^93 + 74*x^91 + 36*x^90 + 11*x^89 + 52*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 76*x^82 + 67*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 21*x^73 + 60*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 68*x^66 + 101*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 55*x^25 + 68*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 60*x^18 + 111*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 49*x^9 + 76*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 52*x^2 + 33*x + 36, x^93 + 74*x^91 + 104*x^90 + 115*x^89 + 120*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 120*x^82 + 91*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 77*x^73 + 40*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 40*x^66 + 45*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 63*x^25 + 88*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 88*x^18 + 103*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 9*x^9 + 8*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 8*x^2 + 73*x + 24, x^93 + 74*x^91 + 12*x^90 + 43*x^89 + 92*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 4*x^82 + 99*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 117*x^73 + 116*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 44*x^66 + 69*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 87*x^25 + 12*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 84*x^18 + 15*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 17*x^9 + 36*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 124*x^2 + x + 108, x^93 + 74*x^91 + 88*x^90 + 115*x^89 + 40*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 8*x^82 + 27*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 77*x^73 + 56*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 88*x^66 + 109*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 63*x^25 + 72*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 40*x^18 + 39*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 9*x^9 + 88*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 120*x^2 + 9*x + 72, x^93 + 74*x^91 + 12*x^90 + 27*x^89 + 76*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 4*x^82 + 115*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 69*x^73 + 68*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 44*x^66 + 117*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 7*x^25 + 60*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 84*x^18 + 95*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 33*x^9 + 52*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 124*x^2 + 113*x + 28, x^93 + 74*x^91 + 80*x^90 + 67*x^89 + 16*x^88 + 4*x^87 + 96*x^86 + x^85 + 96*x^84 + 38*x^83 + 112*x^82 + 75*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 61*x^73 + 48*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 80*x^66 + 125*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 79*x^25 + 80*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 48*x^18 + 23*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 57*x^9 + 112*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 16*x^2 + 89*x + 80, x^93 + 74*x^91 + 28*x^90 + 75*x^89 + 12*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 116*x^82 + 3*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 85*x^73 + 4*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 124*x^66 + 37*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 119*x^25 + 124*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 4*x^18 + 47*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 113*x^9 + 116*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 12*x^2 + 97*x + 28, x^93 + 74*x^91 + 8*x^90 + 67*x^89 + 40*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 88*x^82 + 11*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 61*x^73 + 56*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 72*x^66 + 61*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 79*x^25 + 72*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 56*x^18 + 87*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 57*x^9 + 88*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 40*x^2 + 25*x + 8, x^93 + 74*x^91 + 76*x^90 + 123*x^89 + 108*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 68*x^82 + 19*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 101*x^73 + 36*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 108*x^66 + 85*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 103*x^25 + 92*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 20*x^18 + 127*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 65*x^9 + 20*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 60*x^2 + 81*x + 60, x^93 + 74*x^91 + 96*x^90 + 51*x^89 + 80*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 102*x^83 + 32*x^82 + 91*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 13*x^73 + 112*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 114*x^67 + 96*x^66 + 45*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 127*x^25 + 16*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 30*x^19 + 32*x^18 + 103*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 73*x^9 + 48*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 106*x^3 + 96*x^2 + 73*x + 16, x^93 + 74*x^91 + 120*x^90 + 99*x^89 + 88*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 104*x^82 + 43*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 29*x^73 + 72*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 120*x^66 + 29*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 111*x^25 + 56*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 8*x^18 + 119*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 25*x^9 + 40*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 24*x^2 + 121*x + 56, x^93 + 74*x^91 + 8*x^90 + 35*x^89 + 72*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 24*x^82 + 107*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 93*x^73 + 24*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 8*x^66 + 93*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 47*x^25 + 104*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 120*x^18 + 55*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 89*x^9 + 56*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 104*x^2 + 57*x + 104, x^93 + 74*x^91 + 64*x^90 + 3*x^89 + 96*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 102*x^83 + 75*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 125*x^73 + 32*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 114*x^67 + 125*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 15*x^25 + 96*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 30*x^19 + 23*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 121*x^9 + 32*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 106*x^3 + 89*x + 32, x^93 + 74*x^91 + 16*x^90 + 83*x^89 + 32*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 38*x^83 + 112*x^82 + 123*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 109*x^73 + 96*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 50*x^67 + 80*x^66 + 13*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 31*x^25 + 32*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 94*x^19 + 48*x^18 + 7*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 41*x^9 + 96*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 42*x^3 + 16*x^2 + 41*x + 96, x^93 + 74*x^91 + 88*x^90 + 99*x^89 + 88*x^88 + 68*x^87 + 16*x^86 + x^85 + 80*x^84 + 102*x^83 + 72*x^82 + 107*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 29*x^73 + 72*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 24*x^66 + 93*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 111*x^25 + 56*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 104*x^18 + 55*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 25*x^9 + 40*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 56*x^2 + 57*x + 120, x^93 + 74*x^91 + 116*x^90 + 75*x^89 + 4*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 124*x^82 + 67*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 85*x^73 + 44*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 84*x^66 + 101*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 119*x^25 + 84*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 44*x^18 + 111*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 113*x^9 + 124*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 4*x^2 + 33*x + 116, x^93 + 74*x^91 + 60*x^90 + 59*x^89 + 124*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 84*x^82 + 19*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 37*x^73 + 84*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 28*x^66 + 85*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 39*x^25 + 44*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 100*x^18 + 127*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + x^9 + 4*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 44*x^2 + 81*x + 76, x^93 + 74*x^91 + 84*x^90 + 107*x^89 + 36*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 28*x^82 + 35*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 53*x^73 + 12*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 52*x^66 + 5*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 23*x^25 + 116*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 76*x^18 + 79*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 81*x^9 + 92*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 100*x^2 + 65*x + 20, x^93 + 74*x^91 + 40*x^90 + 35*x^89 + 8*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 120*x^82 + 107*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 93*x^73 + 88*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 40*x^66 + 93*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 47*x^25 + 40*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 88*x^18 + 55*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 89*x^9 + 120*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 8*x^2 + 57*x + 40, x^93 + 74*x^91 + 28*x^90 + 91*x^89 + 124*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 116*x^82 + 115*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 5*x^73 + 84*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 124*x^66 + 117*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 71*x^25 + 44*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 4*x^18 + 95*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 97*x^9 + 4*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 12*x^2 + 113*x + 76, x^93 + 74*x^91 + 44*x^90 + 75*x^89 + 92*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 100*x^82 + 67*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 85*x^73 + 116*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 76*x^66 + 101*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 119*x^25 + 12*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 52*x^18 + 111*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 113*x^9 + 36*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 28*x^2 + 33*x + 108, x^93 + 74*x^91 + 4*x^90 + 91*x^89 + 68*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 44*x^82 + 51*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 5*x^73 + 108*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 100*x^66 + 53*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 71*x^25 + 20*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 28*x^18 + 31*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 97*x^9 + 60*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 84*x^2 + 49*x + 52, x^93 + 74*x^91 + 12*x^90 + 27*x^89 + 12*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 4*x^82 + 115*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 69*x^73 + 4*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 44*x^66 + 117*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 7*x^25 + 124*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 84*x^18 + 95*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 33*x^9 + 116*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 124*x^2 + 113*x + 92, x^93 + 74*x^91 + 4*x^90 + 43*x^89 + 52*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 44*x^82 + 99*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 117*x^73 + 60*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 100*x^66 + 69*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 87*x^25 + 68*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 28*x^18 + 15*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 17*x^9 + 76*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 84*x^2 + x + 100, x^93 + 74*x^91 + 36*x^90 + 43*x^89 + 84*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 76*x^82 + 35*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 117*x^73 + 28*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 68*x^66 + 5*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 87*x^25 + 100*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 60*x^18 + 79*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 17*x^9 + 44*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 52*x^2 + 65*x + 68, x^93 + 74*x^91 + 36*x^90 + 43*x^89 + 52*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 12*x^82 + 99*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 117*x^73 + 60*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 4*x^66 + 69*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 87*x^25 + 68*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 124*x^18 + 15*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 17*x^9 + 76*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 116*x^2 + x + 100, x^93 + 74*x^91 + 72*x^90 + 35*x^89 + 8*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 88*x^82 + 107*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 93*x^73 + 88*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 72*x^66 + 93*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 47*x^25 + 40*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 56*x^18 + 55*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 89*x^9 + 120*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 40*x^2 + 57*x + 40, x^93 + 74*x^91 + 84*x^90 + 27*x^89 + 84*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 92*x^82 + 51*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 69*x^73 + 28*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 116*x^66 + 53*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 7*x^25 + 100*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 12*x^18 + 31*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 33*x^9 + 44*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 36*x^2 + 49*x + 68, x^93 + 74*x^91 + 84*x^90 + 59*x^89 + 52*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 92*x^82 + 19*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 37*x^73 + 60*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 116*x^66 + 85*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 39*x^25 + 68*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 12*x^18 + 127*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + x^9 + 76*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 36*x^2 + 81*x + 36, x^93 + 74*x^91 + 120*x^90 + 35*x^89 + 120*x^88 + 68*x^87 + 80*x^86 + x^85 + 16*x^84 + 102*x^83 + 40*x^82 + 43*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 93*x^73 + 40*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 56*x^66 + 29*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 47*x^25 + 88*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 72*x^18 + 119*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 89*x^9 + 8*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 88*x^2 + 121*x + 24, x^93 + 74*x^91 + 100*x^90 + 11*x^89 + 116*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 12*x^82 + 67*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 21*x^73 + 124*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 4*x^66 + 101*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 55*x^25 + 4*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 124*x^18 + 111*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 49*x^9 + 12*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 116*x^2 + 33*x + 100, x^93 + 74*x^91 + 60*x^90 + 27*x^89 + 28*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 84*x^82 + 51*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 69*x^73 + 52*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 28*x^66 + 53*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 7*x^25 + 76*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 100*x^18 + 31*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 33*x^9 + 100*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 44*x^2 + 49*x + 108, x^93 + 74*x^91 + 16*x^90 + 67*x^89 + 80*x^88 + 4*x^87 + 96*x^86 + x^85 + 96*x^84 + 38*x^83 + 48*x^82 + 75*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 61*x^73 + 112*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 16*x^66 + 125*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 79*x^25 + 16*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 112*x^18 + 23*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 57*x^9 + 48*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 80*x^2 + 89*x + 16, x^93 + 74*x^91 + 52*x^90 + 11*x^89 + 68*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 124*x^82 + 67*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 21*x^73 + 108*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 84*x^66 + 101*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 55*x^25 + 20*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 44*x^18 + 111*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 49*x^9 + 60*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 4*x^2 + 33*x + 116, x^93 + 74*x^91 + 20*x^90 + 91*x^89 + 20*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 92*x^82 + 51*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 5*x^73 + 92*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 116*x^66 + 53*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 71*x^25 + 36*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 12*x^18 + 31*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 97*x^9 + 108*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 36*x^2 + 49*x + 68, x^93 + 74*x^91 + 104*x^90 + 67*x^89 + 72*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 120*x^82 + 11*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 61*x^73 + 24*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 40*x^66 + 61*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 79*x^25 + 104*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 88*x^18 + 87*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 57*x^9 + 56*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 8*x^2 + 25*x + 40, x^93 + 74*x^91 + 60*x^90 + 107*x^89 + 76*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 20*x^82 + 35*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 53*x^73 + 68*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 92*x^66 + 5*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 23*x^25 + 60*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 36*x^18 + 79*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 81*x^9 + 52*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 108*x^2 + 65*x + 28, x^93 + 74*x^91 + 80*x^90 + 67*x^89 + 80*x^88 + 4*x^87 + 96*x^86 + x^85 + 96*x^84 + 38*x^83 + 112*x^82 + 75*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 61*x^73 + 112*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 80*x^66 + 125*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 79*x^25 + 16*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 48*x^18 + 23*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 57*x^9 + 48*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 16*x^2 + 89*x + 16, x^93 + 74*x^91 + 92*x^90 + 43*x^89 + 12*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 116*x^82 + 99*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 117*x^73 + 4*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 124*x^66 + 69*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 87*x^25 + 124*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 4*x^18 + 15*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 17*x^9 + 116*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 12*x^2 + x + 92, x^93 + 74*x^91 + 104*x^90 + 115*x^89 + 24*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 56*x^82 + 27*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 77*x^73 + 8*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 104*x^66 + 109*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 63*x^25 + 120*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 24*x^18 + 39*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 9*x^9 + 104*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 72*x^2 + 9*x + 120, x^93 + 74*x^91 + 36*x^90 + 11*x^89 + 20*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 12*x^82 + 3*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 21*x^73 + 92*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 4*x^66 + 37*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 55*x^25 + 36*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 124*x^18 + 47*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 49*x^9 + 108*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 116*x^2 + 97*x + 68, x^93 + 74*x^91 + 40*x^90 + 115*x^89 + 120*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 56*x^82 + 91*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 77*x^73 + 40*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 104*x^66 + 45*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 63*x^25 + 88*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 24*x^18 + 103*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 9*x^9 + 8*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 72*x^2 + 73*x + 24, x^93 + 74*x^91 + 20*x^90 + 43*x^89 + 100*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 28*x^82 + 35*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 117*x^73 + 76*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 52*x^66 + 5*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 87*x^25 + 52*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 76*x^18 + 79*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 17*x^9 + 28*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 100*x^2 + 65*x + 20, x^93 + 74*x^91 + 88*x^90 + 99*x^89 + 120*x^88 + 68*x^87 + 16*x^86 + x^85 + 16*x^84 + 102*x^83 + 72*x^82 + 107*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 29*x^73 + 40*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 24*x^66 + 93*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 111*x^25 + 88*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 104*x^18 + 55*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 25*x^9 + 8*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 56*x^2 + 57*x + 24, x^93 + 74*x^91 + 16*x^90 + 83*x^89 + 96*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 48*x^82 + 59*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 109*x^73 + 32*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 16*x^66 + 77*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 31*x^25 + 96*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 112*x^18 + 71*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 41*x^9 + 32*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 80*x^2 + 105*x + 96, x^93 + 74*x^91 + 108*x^90 + 43*x^89 + 124*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 36*x^82 + 99*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 117*x^73 + 84*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 12*x^66 + 69*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 87*x^25 + 44*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 116*x^18 + 15*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 17*x^9 + 4*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 92*x^2 + x + 12, x^93 + 74*x^91 + 116*x^90 + 43*x^89 + 100*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 124*x^82 + 99*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 117*x^73 + 76*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 84*x^66 + 69*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 87*x^25 + 52*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 44*x^18 + 15*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 17*x^9 + 28*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 4*x^2 + x + 84, x^93 + 74*x^91 + 100*x^90 + 27*x^89 + 68*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 76*x^82 + 115*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 69*x^73 + 108*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 68*x^66 + 117*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 7*x^25 + 20*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 60*x^18 + 95*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 33*x^9 + 60*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 52*x^2 + 113*x + 52, x^93 + 74*x^91 + 120*x^90 + 115*x^89 + 8*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 104*x^82 + 27*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 77*x^73 + 88*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 120*x^66 + 109*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 63*x^25 + 40*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 8*x^18 + 39*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 9*x^9 + 120*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 24*x^2 + 9*x + 40, x^93 + 74*x^91 + 108*x^90 + 75*x^89 + 124*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 36*x^82 + 67*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 85*x^73 + 84*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 12*x^66 + 101*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 119*x^25 + 44*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 116*x^18 + 111*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 113*x^9 + 4*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 92*x^2 + 33*x + 12, x^93 + 74*x^91 + 67*x^89 + 32*x^88 + 4*x^87 + x^85 + 64*x^84 + 38*x^83 + 75*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 61*x^73 + 96*x^72 + 52*x^71 + 7*x^69 + 64*x^68 + 50*x^67 + 125*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 79*x^25 + 32*x^24 + 52*x^23 + 37*x^21 + 64*x^20 + 94*x^19 + 23*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 57*x^9 + 96*x^8 + 4*x^7 + 27*x^5 + 64*x^4 + 42*x^3 + 89*x + 32, x^93 + 74*x^91 + 44*x^90 + 27*x^89 + 12*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 36*x^82 + 51*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 69*x^73 + 4*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 12*x^66 + 53*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 7*x^25 + 124*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 116*x^18 + 31*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 33*x^9 + 116*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 92*x^2 + 49*x + 28, x^93 + 74*x^91 + 68*x^90 + 27*x^89 + 36*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 108*x^82 + 115*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 69*x^73 + 12*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 36*x^66 + 117*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 7*x^25 + 116*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 92*x^18 + 95*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 33*x^9 + 92*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 20*x^2 + 113*x + 20, x^93 + 74*x^91 + 48*x^90 + 83*x^89 + 64*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 102*x^83 + 16*x^82 + 59*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 109*x^73 + 64*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 114*x^67 + 48*x^66 + 77*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 31*x^25 + 64*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 30*x^19 + 80*x^18 + 71*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 41*x^9 + 64*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 106*x^3 + 112*x^2 + 105*x + 64, x^93 + 74*x^91 + 88*x^90 + 51*x^89 + 8*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 72*x^82 + 27*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 13*x^73 + 88*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 24*x^66 + 109*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 127*x^25 + 40*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 104*x^18 + 39*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 73*x^9 + 120*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 56*x^2 + 9*x + 104, x^93 + 74*x^91 + 20*x^90 + 27*x^89 + 84*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 92*x^82 + 115*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 69*x^73 + 28*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 116*x^66 + 117*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 7*x^25 + 100*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 12*x^18 + 95*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 33*x^9 + 44*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 36*x^2 + 113*x + 4, x^93 + 74*x^91 + 100*x^90 + 107*x^89 + 116*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 76*x^82 + 35*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 53*x^73 + 124*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 68*x^66 + 5*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 23*x^25 + 4*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 60*x^18 + 79*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 81*x^9 + 12*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 52*x^2 + 65*x + 36, x^93 + 74*x^91 + 124*x^90 + 27*x^89 + 60*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 84*x^82 + 115*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 69*x^73 + 20*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 28*x^66 + 117*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 7*x^25 + 108*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 100*x^18 + 95*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 33*x^9 + 68*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 44*x^2 + 113*x + 76, x^93 + 74*x^91 + 48*x^90 + 3*x^89 + 112*x^88 + 4*x^87 + 32*x^86 + x^85 + 32*x^84 + 38*x^83 + 16*x^82 + 11*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 125*x^73 + 80*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 48*x^66 + 61*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 15*x^25 + 48*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 80*x^18 + 87*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 121*x^9 + 16*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 112*x^2 + 25*x + 48, x^93 + 74*x^91 + 80*x^90 + 3*x^89 + 112*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 48*x^82 + 75*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 125*x^73 + 80*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 16*x^66 + 125*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 15*x^25 + 48*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 112*x^18 + 23*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 121*x^9 + 16*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 80*x^2 + 89*x + 112, x^93 + 74*x^91 + 68*x^90 + 27*x^89 + 100*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 108*x^82 + 115*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 69*x^73 + 76*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 36*x^66 + 117*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 7*x^25 + 52*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 92*x^18 + 95*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 33*x^9 + 28*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 20*x^2 + 113*x + 84, x^93 + 74*x^91 + 88*x^90 + 3*x^89 + 88*x^88 + 4*x^87 + 80*x^86 + x^85 + 16*x^84 + 38*x^83 + 8*x^82 + 11*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 125*x^73 + 72*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 88*x^66 + 61*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 15*x^25 + 56*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 40*x^18 + 87*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 121*x^9 + 40*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 120*x^2 + 25*x + 56, x^93 + 74*x^91 + 8*x^90 + 99*x^89 + 72*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 24*x^82 + 43*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 29*x^73 + 24*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 8*x^66 + 29*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 111*x^25 + 104*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 120*x^18 + 119*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 25*x^9 + 56*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 104*x^2 + 121*x + 104, x^93 + 74*x^91 + 56*x^90 + 51*x^89 + 40*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 40*x^82 + 91*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 13*x^73 + 56*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 56*x^66 + 45*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 127*x^25 + 72*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 72*x^18 + 103*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 73*x^9 + 88*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 88*x^2 + 73*x + 72, x^93 + 74*x^91 + 44*x^90 + 27*x^89 + 12*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 100*x^82 + 115*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 69*x^73 + 4*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 76*x^66 + 117*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 7*x^25 + 124*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 52*x^18 + 95*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 33*x^9 + 116*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 28*x^2 + 113*x + 92, x^93 + 74*x^91 + 48*x^90 + 51*x^89 + 68*x^87 + 32*x^86 + 97*x^85 + 102*x^83 + 16*x^82 + 91*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 13*x^73 + 116*x^71 + 32*x^70 + 103*x^69 + 114*x^67 + 48*x^66 + 45*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 127*x^25 + 116*x^23 + 32*x^22 + 5*x^21 + 30*x^19 + 80*x^18 + 103*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 73*x^9 + 68*x^7 + 32*x^6 + 123*x^5 + 106*x^3 + 112*x^2 + 73*x, x^93 + 74*x^91 + 56*x^90 + 3*x^89 + 56*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 104*x^82 + 75*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 125*x^73 + 104*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 120*x^66 + 125*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 15*x^25 + 24*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 8*x^18 + 23*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 121*x^9 + 72*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 24*x^2 + 89*x + 88, x^93 + 74*x^91 + 80*x^90 + 99*x^89 + 48*x^88 + 68*x^87 + 32*x^86 + x^85 + 96*x^84 + 102*x^83 + 48*x^82 + 107*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 29*x^73 + 16*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 16*x^66 + 93*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 111*x^25 + 112*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 112*x^18 + 55*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 25*x^9 + 80*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 80*x^2 + 57*x + 48, x^93 + 74*x^91 + 64*x^90 + 51*x^89 + 112*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 38*x^83 + 27*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 13*x^73 + 80*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 50*x^67 + 109*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 127*x^25 + 48*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 94*x^19 + 39*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 73*x^9 + 16*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 42*x^3 + 9*x + 112, x^93 + 74*x^91 + 8*x^90 + 115*x^89 + 120*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 88*x^82 + 91*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 77*x^73 + 40*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 72*x^66 + 45*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 63*x^25 + 88*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 56*x^18 + 103*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 9*x^9 + 8*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 40*x^2 + 73*x + 24, x^93 + 74*x^91 + 92*x^90 + 59*x^89 + 124*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 116*x^82 + 83*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 37*x^73 + 84*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 124*x^66 + 21*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 39*x^25 + 44*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 4*x^18 + 63*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + x^9 + 4*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 12*x^2 + 17*x + 12, x^93 + 74*x^91 + 8*x^90 + 67*x^89 + 72*x^88 + 4*x^87 + 112*x^86 + x^85 + 48*x^84 + 38*x^83 + 24*x^82 + 75*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 61*x^73 + 24*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 8*x^66 + 125*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 79*x^25 + 104*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 120*x^18 + 23*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 57*x^9 + 56*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 104*x^2 + 89*x + 104, x^93 + 74*x^91 + 92*x^90 + 75*x^89 + 12*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 116*x^82 + 67*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 85*x^73 + 4*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 124*x^66 + 101*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 119*x^25 + 124*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 4*x^18 + 111*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 113*x^9 + 116*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 12*x^2 + 33*x + 92, x^93 + 74*x^91 + 40*x^90 + 19*x^89 + 120*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 56*x^82 + 59*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 45*x^73 + 40*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 104*x^66 + 77*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 95*x^25 + 88*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 24*x^18 + 71*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 105*x^9 + 8*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 72*x^2 + 105*x + 24, x^93 + 74*x^91 + 92*x^90 + 27*x^89 + 124*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 116*x^82 + 115*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 69*x^73 + 84*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 124*x^66 + 117*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 7*x^25 + 44*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 4*x^18 + 95*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 33*x^9 + 4*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 12*x^2 + 113*x + 12, x^93 + 74*x^91 + 32*x^90 + 83*x^89 + 48*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 102*x^83 + 96*x^82 + 59*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 109*x^73 + 16*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 114*x^67 + 32*x^66 + 77*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 31*x^25 + 112*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 30*x^19 + 96*x^18 + 71*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 41*x^9 + 80*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 106*x^3 + 32*x^2 + 105*x + 112, x^93 + 74*x^91 + 68*x^90 + 75*x^89 + 116*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 108*x^82 + 67*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 85*x^73 + 124*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 36*x^66 + 101*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 119*x^25 + 4*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 92*x^18 + 111*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 113*x^9 + 12*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 20*x^2 + 33*x + 36, x^93 + 74*x^91 + 40*x^90 + 67*x^89 + 8*x^88 + 4*x^87 + 48*x^86 + x^85 + 48*x^84 + 38*x^83 + 120*x^82 + 75*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 61*x^73 + 88*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 40*x^66 + 125*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 79*x^25 + 40*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 88*x^18 + 23*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 57*x^9 + 120*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 8*x^2 + 89*x + 40, x^93 + 74*x^91 + 80*x^90 + 83*x^89 + 96*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 112*x^82 + 59*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 109*x^73 + 32*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 80*x^66 + 77*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 31*x^25 + 96*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 48*x^18 + 71*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 41*x^9 + 32*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 16*x^2 + 105*x + 96, x^93 + 74*x^91 + 112*x^90 + 35*x^89 + 48*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 80*x^82 + 107*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 93*x^73 + 16*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 112*x^66 + 93*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 47*x^25 + 112*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 16*x^18 + 55*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 89*x^9 + 80*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 48*x^2 + 57*x + 112, x^93 + 74*x^91 + 19*x^89 + 112*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 38*x^83 + 64*x^82 + 59*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 45*x^73 + 80*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 50*x^67 + 64*x^66 + 77*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 95*x^25 + 48*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 94*x^19 + 64*x^18 + 71*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 105*x^9 + 16*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 42*x^3 + 64*x^2 + 105*x + 112, x^93 + 74*x^91 + 124*x^90 + 43*x^89 + 12*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 20*x^82 + 35*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 117*x^73 + 4*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 92*x^66 + 5*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 87*x^25 + 124*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 36*x^18 + 79*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 17*x^9 + 116*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 108*x^2 + 65*x + 28, x^93 + 74*x^91 + 80*x^90 + 19*x^89 + 4*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 48*x^82 + 59*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 45*x^73 + 52*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 16*x^66 + 77*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 95*x^25 + 52*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 112*x^18 + 71*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 105*x^9 + 4*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 80*x^2 + 105*x + 64, x^93 + 74*x^91 + 20*x^90 + 123*x^89 + 20*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 28*x^82 + 83*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 101*x^73 + 92*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 52*x^66 + 21*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 103*x^25 + 36*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 76*x^18 + 63*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 65*x^9 + 108*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 100*x^2 + 17*x + 4, x^93 + 74*x^91 + 56*x^90 + 3*x^89 + 56*x^88 + 4*x^87 + 16*x^86 + x^85 + 80*x^84 + 38*x^83 + 40*x^82 + 11*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 125*x^73 + 104*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 56*x^66 + 61*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 15*x^25 + 24*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 72*x^18 + 87*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 121*x^9 + 72*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 88*x^2 + 25*x + 24, x^93 + 74*x^91 + 88*x^90 + 99*x^89 + 24*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 8*x^82 + 43*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 29*x^73 + 8*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 88*x^66 + 29*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 111*x^25 + 120*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 40*x^18 + 119*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 25*x^9 + 104*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 120*x^2 + 121*x + 120, x^93 + 74*x^91 + 44*x^90 + 107*x^89 + 60*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 36*x^82 + 99*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 53*x^73 + 20*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 12*x^66 + 69*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 23*x^25 + 108*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 116*x^18 + 15*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 81*x^9 + 68*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 92*x^2 + x + 12, x^93 + 74*x^91 + 88*x^90 + 83*x^89 + 8*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 8*x^82 + 59*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 109*x^73 + 88*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 88*x^66 + 77*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 31*x^25 + 40*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 40*x^18 + 71*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 41*x^9 + 120*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 120*x^2 + 105*x + 40, x^93 + 74*x^91 + 36*x^90 + 107*x^89 + 84*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 76*x^82 + 99*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 53*x^73 + 28*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 68*x^66 + 69*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 23*x^25 + 100*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 60*x^18 + 15*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 81*x^9 + 44*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 52*x^2 + x + 68, x^93 + 74*x^91 + 116*x^90 + 11*x^89 + 68*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 124*x^82 + 3*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 21*x^73 + 108*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 84*x^66 + 37*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 55*x^25 + 20*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 44*x^18 + 47*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 49*x^9 + 60*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 4*x^2 + 97*x + 52, x^93 + 74*x^91 + 72*x^90 + 67*x^89 + 8*x^88 + 4*x^87 + 112*x^86 + x^85 + 48*x^84 + 38*x^83 + 88*x^82 + 75*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 61*x^73 + 88*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 72*x^66 + 125*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 79*x^25 + 40*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 56*x^18 + 23*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 57*x^9 + 120*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 40*x^2 + 89*x + 40, x^93 + 74*x^91 + 44*x^90 + 123*x^89 + 44*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 100*x^82 + 19*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 101*x^73 + 100*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 76*x^66 + 85*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 103*x^25 + 28*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 52*x^18 + 127*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 65*x^9 + 84*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 28*x^2 + 81*x + 124, x^93 + 74*x^91 + 60*x^90 + 107*x^89 + 12*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 84*x^82 + 99*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 53*x^73 + 4*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 28*x^66 + 69*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 23*x^25 + 124*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 100*x^18 + 15*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 81*x^9 + 116*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 44*x^2 + x + 28, x^93 + 74*x^91 + 24*x^90 + 35*x^89 + 24*x^88 + 68*x^87 + 16*x^86 + x^85 + 80*x^84 + 102*x^83 + 8*x^82 + 43*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 93*x^73 + 8*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 88*x^66 + 29*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 47*x^25 + 120*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 40*x^18 + 119*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 89*x^9 + 104*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 120*x^2 + 121*x + 56, x^93 + 74*x^91 + 72*x^90 + 83*x^89 + 88*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 88*x^82 + 59*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 109*x^73 + 72*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 72*x^66 + 77*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 31*x^25 + 56*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 56*x^18 + 71*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 41*x^9 + 40*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 40*x^2 + 105*x + 56, x^93 + 74*x^91 + 64*x^90 + 51*x^89 + 112*x^88 + 68*x^87 + 97*x^85 + 32*x^84 + 102*x^83 + 64*x^82 + 91*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 13*x^73 + 80*x^72 + 116*x^71 + 103*x^69 + 32*x^68 + 114*x^67 + 64*x^66 + 45*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 127*x^25 + 48*x^24 + 116*x^23 + 5*x^21 + 32*x^20 + 30*x^19 + 64*x^18 + 103*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 73*x^9 + 16*x^8 + 68*x^7 + 123*x^5 + 32*x^4 + 106*x^3 + 64*x^2 + 73*x + 48, x^93 + 74*x^91 + 116*x^90 + 59*x^89 + 52*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 124*x^82 + 83*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 37*x^73 + 60*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 84*x^66 + 21*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 39*x^25 + 68*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 44*x^18 + 63*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + x^9 + 76*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 4*x^2 + 17*x + 100, x^93 + 74*x^91 + 92*x^90 + 11*x^89 + 76*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 116*x^82 + 3*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 21*x^73 + 68*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 124*x^66 + 37*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 55*x^25 + 60*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 4*x^18 + 47*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 49*x^9 + 52*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 12*x^2 + 97*x + 28, x^93 + 74*x^91 + 115*x^89 + 80*x^88 + 68*x^87 + 97*x^85 + 96*x^84 + 102*x^83 + 27*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 77*x^73 + 112*x^72 + 116*x^71 + 103*x^69 + 96*x^68 + 114*x^67 + 109*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 63*x^25 + 16*x^24 + 116*x^23 + 5*x^21 + 96*x^20 + 30*x^19 + 39*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 9*x^9 + 48*x^8 + 68*x^7 + 123*x^5 + 96*x^4 + 106*x^3 + 9*x + 16, x^93 + 74*x^91 + 116*x^90 + 11*x^89 + 100*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 60*x^82 + 67*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 21*x^73 + 76*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 20*x^66 + 101*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 55*x^25 + 52*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 108*x^18 + 111*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 49*x^9 + 28*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 68*x^2 + 33*x + 20, x^93 + 74*x^91 + 80*x^90 + 19*x^89 + 32*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 112*x^82 + 123*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 45*x^73 + 96*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 80*x^66 + 13*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 95*x^25 + 32*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 48*x^18 + 7*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 105*x^9 + 96*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 16*x^2 + 41*x + 32, x^93 + 74*x^91 + 24*x^90 + 51*x^89 + 72*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 8*x^82 + 27*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 13*x^73 + 24*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 88*x^66 + 109*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 127*x^25 + 104*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 40*x^18 + 39*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 73*x^9 + 56*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 120*x^2 + 9*x + 40, x^93 + 74*x^91 + 108*x^90 + 11*x^89 + 124*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 36*x^82 + 3*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 21*x^73 + 84*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 12*x^66 + 37*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 55*x^25 + 44*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 116*x^18 + 47*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 49*x^9 + 4*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 92*x^2 + 97*x + 12, x^93 + 74*x^91 + 36*x^90 + 123*x^89 + 4*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 76*x^82 + 83*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 101*x^73 + 44*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 68*x^66 + 21*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 103*x^25 + 84*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 60*x^18 + 63*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 65*x^9 + 124*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 52*x^2 + 17*x + 52, x^93 + 74*x^91 + 32*x^90 + 83*x^89 + 16*x^88 + 4*x^87 + 97*x^85 + 32*x^84 + 38*x^83 + 32*x^82 + 123*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 109*x^73 + 48*x^72 + 52*x^71 + 103*x^69 + 32*x^68 + 50*x^67 + 96*x^66 + 13*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 31*x^25 + 80*x^24 + 52*x^23 + 5*x^21 + 32*x^20 + 94*x^19 + 32*x^18 + 7*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 41*x^9 + 112*x^8 + 4*x^7 + 123*x^5 + 32*x^4 + 42*x^3 + 96*x^2 + 41*x + 16, x^93 + 74*x^91 + 24*x^90 + 35*x^89 + 120*x^88 + 68*x^87 + 16*x^86 + x^85 + 16*x^84 + 102*x^83 + 8*x^82 + 43*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 93*x^73 + 40*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 88*x^66 + 29*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 47*x^25 + 88*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 40*x^18 + 119*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 89*x^9 + 8*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 120*x^2 + 121*x + 24, x^93 + 74*x^91 + 104*x^90 + 83*x^89 + 56*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 120*x^82 + 123*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 109*x^73 + 104*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 40*x^66 + 13*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 31*x^25 + 24*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 88*x^18 + 7*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 41*x^9 + 72*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 8*x^2 + 41*x + 88, x^93 + 74*x^91 + 56*x^90 + 115*x^89 + 8*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 40*x^82 + 27*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 77*x^73 + 88*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 56*x^66 + 109*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 63*x^25 + 40*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 72*x^18 + 39*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 9*x^9 + 120*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 88*x^2 + 9*x + 40, x^93 + 74*x^91 + 44*x^90 + 27*x^89 + 44*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 36*x^82 + 51*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 69*x^73 + 100*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 12*x^66 + 53*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 7*x^25 + 28*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 116*x^18 + 31*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 33*x^9 + 84*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 92*x^2 + 49*x + 60, x^93 + 74*x^91 + 48*x^90 + 35*x^89 + 112*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 16*x^82 + 107*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 93*x^73 + 80*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 48*x^66 + 93*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 47*x^25 + 48*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 80*x^18 + 55*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 89*x^9 + 16*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 112*x^2 + 57*x + 48, x^93 + 74*x^91 + 60*x^90 + 75*x^89 + 108*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 20*x^82 + 67*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 85*x^73 + 36*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 92*x^66 + 101*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 119*x^25 + 92*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 36*x^18 + 111*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 113*x^9 + 20*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 108*x^2 + 33*x + 60, x^93 + 74*x^91 + 24*x^90 + 115*x^89 + 8*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 72*x^82 + 27*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 77*x^73 + 88*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 24*x^66 + 109*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 63*x^25 + 40*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 104*x^18 + 39*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 9*x^9 + 120*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 56*x^2 + 9*x + 40, x^93 + 74*x^91 + 116*x^90 + 59*x^89 + 20*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 124*x^82 + 83*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 37*x^73 + 92*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 84*x^66 + 21*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 39*x^25 + 36*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 44*x^18 + 63*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + x^9 + 108*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 4*x^2 + 17*x + 68, x^93 + 74*x^91 + 36*x^90 + 75*x^89 + 20*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 12*x^82 + 67*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 85*x^73 + 92*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 4*x^66 + 101*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 119*x^25 + 36*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 124*x^18 + 111*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 113*x^9 + 108*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 116*x^2 + 33*x + 68, x^93 + 74*x^91 + 44*x^90 + 43*x^89 + 60*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 100*x^82 + 99*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 117*x^73 + 20*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 76*x^66 + 69*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 87*x^25 + 108*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 52*x^18 + 15*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 17*x^9 + 68*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 28*x^2 + x + 76, x^93 + 74*x^91 + 80*x^90 + 67*x^89 + 48*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 48*x^82 + 11*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 61*x^73 + 16*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 16*x^66 + 61*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 79*x^25 + 112*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 112*x^18 + 87*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 57*x^9 + 80*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 80*x^2 + 25*x + 48, x^93 + 74*x^91 + 56*x^90 + 99*x^89 + 56*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 40*x^82 + 43*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 29*x^73 + 104*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 56*x^66 + 29*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 111*x^25 + 24*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 72*x^18 + 119*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 25*x^9 + 72*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 88*x^2 + 121*x + 24, x^93 + 74*x^91 + 116*x^90 + 107*x^89 + 68*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 60*x^82 + 99*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 53*x^73 + 108*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 20*x^66 + 69*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 23*x^25 + 20*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 108*x^18 + 15*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 81*x^9 + 60*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 68*x^2 + x + 116, x^93 + 74*x^91 + 72*x^90 + 51*x^89 + 88*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 88*x^82 + 91*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 13*x^73 + 72*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 72*x^66 + 45*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 127*x^25 + 56*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 56*x^18 + 103*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 73*x^9 + 40*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 40*x^2 + 73*x + 56, x^93 + 74*x^91 + 104*x^90 + 99*x^89 + 72*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 56*x^82 + 43*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 29*x^73 + 24*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 104*x^66 + 29*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 111*x^25 + 104*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 24*x^18 + 119*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 25*x^9 + 56*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 72*x^2 + 121*x + 104, x^93 + 74*x^91 + 44*x^90 + 75*x^89 + 60*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 36*x^82 + 3*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 85*x^73 + 20*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 12*x^66 + 37*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 119*x^25 + 108*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 116*x^18 + 47*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 113*x^9 + 68*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 92*x^2 + 97*x + 12, x^93 + 74*x^91 + 108*x^90 + 27*x^89 + 76*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 36*x^82 + 115*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 69*x^73 + 68*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 12*x^66 + 117*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 7*x^25 + 60*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 116*x^18 + 95*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 33*x^9 + 52*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 92*x^2 + 113*x + 28, x^93 + 74*x^91 + 12*x^90 + 123*x^89 + 44*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 4*x^82 + 19*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 101*x^73 + 100*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 44*x^66 + 85*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 103*x^25 + 28*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 84*x^18 + 127*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 65*x^9 + 84*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 124*x^2 + 81*x + 124, x^93 + 74*x^91 + 104*x^90 + 19*x^89 + 120*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 56*x^82 + 123*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 45*x^73 + 40*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 104*x^66 + 13*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 95*x^25 + 88*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 24*x^18 + 7*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 105*x^9 + 8*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 72*x^2 + 41*x + 88, x^93 + 74*x^91 + 68*x^90 + 11*x^89 + 20*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 108*x^82 + 3*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 21*x^73 + 92*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 36*x^66 + 37*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 55*x^25 + 36*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 92*x^18 + 47*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 49*x^9 + 108*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 20*x^2 + 97*x + 68, x^93 + 74*x^91 + 19*x^89 + 48*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 38*x^83 + 64*x^82 + 59*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 45*x^73 + 16*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 50*x^67 + 64*x^66 + 77*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 95*x^25 + 112*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 94*x^19 + 64*x^18 + 71*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 105*x^9 + 80*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 42*x^3 + 64*x^2 + 105*x + 48, x^93 + 74*x^91 + 48*x^90 + 115*x^89 + 32*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 16*x^82 + 27*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 77*x^73 + 96*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 48*x^66 + 109*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 63*x^25 + 32*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 80*x^18 + 39*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 9*x^9 + 96*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 112*x^2 + 9*x + 32, x^93 + 74*x^91 + 112*x^90 + 83*x^89 + 64*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 102*x^83 + 80*x^82 + 59*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 109*x^73 + 64*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 114*x^67 + 112*x^66 + 77*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 31*x^25 + 64*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 30*x^19 + 16*x^18 + 71*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 41*x^9 + 64*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 106*x^3 + 48*x^2 + 105*x + 64, x^93 + 74*x^91 + 32*x^90 + 35*x^89 + 96*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 38*x^83 + 96*x^82 + 107*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 93*x^73 + 32*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 50*x^67 + 32*x^66 + 93*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 47*x^25 + 96*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 94*x^19 + 96*x^18 + 55*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 42*x^3 + 32*x^2 + 57*x + 96, x^93 + 74*x^91 + 20*x^90 + 11*x^89 + 36*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 28*x^82 + 67*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 21*x^73 + 12*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 52*x^66 + 101*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 55*x^25 + 116*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 76*x^18 + 111*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 49*x^9 + 92*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 100*x^2 + 33*x + 84, x^93 + 74*x^91 + 68*x^90 + 59*x^89 + 4*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 44*x^82 + 19*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 37*x^73 + 44*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 100*x^66 + 85*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 39*x^25 + 84*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 28*x^18 + 127*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + x^9 + 124*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 84*x^2 + 81*x + 52, x^93 + 74*x^91 + 12*x^90 + 11*x^89 + 92*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 68*x^82 + 67*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 21*x^73 + 116*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 108*x^66 + 101*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 55*x^25 + 12*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 20*x^18 + 111*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 49*x^9 + 36*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 60*x^2 + 33*x + 44, x^93 + 74*x^91 + 99*x^89 + 96*x^88 + 4*x^87 + 65*x^85 + 64*x^84 + 38*x^83 + 43*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 29*x^73 + 32*x^72 + 52*x^71 + 71*x^69 + 64*x^68 + 50*x^67 + 29*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 111*x^25 + 96*x^24 + 52*x^23 + 101*x^21 + 64*x^20 + 94*x^19 + 119*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 25*x^9 + 32*x^8 + 4*x^7 + 91*x^5 + 64*x^4 + 42*x^3 + 121*x + 96, x^93 + 74*x^91 + 68*x^90 + 75*x^89 + 84*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 108*x^82 + 67*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 85*x^73 + 28*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 36*x^66 + 101*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 119*x^25 + 100*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 92*x^18 + 111*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 113*x^9 + 44*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 20*x^2 + 33*x + 4, x^93 + 74*x^91 + 76*x^90 + 59*x^89 + 76*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 68*x^82 + 83*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 37*x^73 + 68*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 108*x^66 + 21*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 39*x^25 + 60*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 20*x^18 + 63*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + x^9 + 52*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 60*x^2 + 17*x + 28, x^93 + 74*x^91 + 48*x^90 + 67*x^89 + 80*x^88 + 4*x^87 + 32*x^86 + x^85 + 96*x^84 + 38*x^83 + 16*x^82 + 75*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 61*x^73 + 112*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 48*x^66 + 125*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 79*x^25 + 16*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 80*x^18 + 23*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 57*x^9 + 48*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 112*x^2 + 89*x + 16, x^93 + 74*x^91 + 48*x^90 + 83*x^89 + 4*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 80*x^82 + 123*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 109*x^73 + 52*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 112*x^66 + 13*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 31*x^25 + 52*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 16*x^18 + 7*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 41*x^9 + 4*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 48*x^2 + 41*x + 64, x^93 + 74*x^91 + 52*x^90 + 123*x^89 + 84*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 124*x^82 + 83*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 101*x^73 + 28*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 84*x^66 + 21*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 103*x^25 + 100*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 44*x^18 + 63*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 65*x^9 + 44*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 4*x^2 + 17*x + 68, x^93 + 74*x^91 + 84*x^90 + 27*x^89 + 52*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 28*x^82 + 115*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 69*x^73 + 60*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 52*x^66 + 117*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 7*x^25 + 68*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 76*x^18 + 95*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 33*x^9 + 76*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 100*x^2 + 113*x + 100, x^93 + 74*x^91 + 68*x^90 + 75*x^89 + 52*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 44*x^82 + 3*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 85*x^73 + 60*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 100*x^66 + 37*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 119*x^25 + 68*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 28*x^18 + 47*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 113*x^9 + 76*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 84*x^2 + 97*x + 36, x^93 + 74*x^91 + 12*x^90 + 43*x^89 + 60*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 68*x^82 + 35*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 117*x^73 + 20*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 108*x^66 + 5*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 87*x^25 + 108*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 20*x^18 + 79*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 17*x^9 + 68*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 60*x^2 + 65*x + 12, x^93 + 74*x^91 + 68*x^90 + 43*x^89 + 84*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 108*x^82 + 99*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 117*x^73 + 28*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 36*x^66 + 69*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 87*x^25 + 100*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 92*x^18 + 15*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 17*x^9 + 44*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 20*x^2 + x + 4, x^93 + 74*x^91 + 24*x^90 + 35*x^89 + 120*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 72*x^82 + 107*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 93*x^73 + 40*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 24*x^66 + 93*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 47*x^25 + 88*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 104*x^18 + 55*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 89*x^9 + 8*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 56*x^2 + 57*x + 88, x^93 + 74*x^91 + 116*x^90 + 123*x^89 + 84*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 124*x^82 + 19*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 101*x^73 + 28*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 84*x^66 + 85*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 103*x^25 + 100*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 44*x^18 + 127*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 65*x^9 + 44*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 4*x^2 + 81*x + 4, x^93 + 74*x^91 + 12*x^90 + 107*x^89 + 124*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 4*x^82 + 35*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 53*x^73 + 84*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 44*x^66 + 5*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 23*x^25 + 44*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 84*x^18 + 79*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 81*x^9 + 4*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 124*x^2 + 65*x + 12, x^93 + 74*x^91 + 112*x^90 + 35*x^89 + 80*x^88 + 68*x^87 + 96*x^86 + x^85 + 32*x^84 + 102*x^83 + 16*x^82 + 43*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 93*x^73 + 112*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 48*x^66 + 29*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 47*x^25 + 16*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 80*x^18 + 119*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 89*x^9 + 48*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 112*x^2 + 121*x + 80, x^93 + 74*x^91 + 72*x^90 + 19*x^89 + 24*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 24*x^82 + 59*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 45*x^73 + 8*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 8*x^66 + 77*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 95*x^25 + 120*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 120*x^18 + 71*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 105*x^9 + 104*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 104*x^2 + 105*x + 56, x^93 + 74*x^91 + 83*x^89 + 112*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 38*x^83 + 64*x^82 + 123*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 109*x^73 + 80*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 50*x^67 + 64*x^66 + 13*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 31*x^25 + 48*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 94*x^19 + 64*x^18 + 7*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 41*x^9 + 16*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 42*x^3 + 64*x^2 + 41*x + 112, x^93 + 74*x^91 + 12*x^90 + 59*x^89 + 44*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 4*x^82 + 83*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 37*x^73 + 100*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 44*x^66 + 21*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 39*x^25 + 28*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 84*x^18 + 63*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + x^9 + 84*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 124*x^2 + 17*x + 124, x^93 + 74*x^91 + 124*x^90 + 43*x^89 + 44*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 20*x^82 + 35*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 117*x^73 + 100*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 92*x^66 + 5*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 87*x^25 + 28*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 36*x^18 + 79*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 17*x^9 + 84*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 108*x^2 + 65*x + 60, x^93 + 74*x^91 + 116*x^90 + 11*x^89 + 36*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 124*x^82 + 3*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 21*x^73 + 12*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 84*x^66 + 37*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 55*x^25 + 116*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 44*x^18 + 47*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 49*x^9 + 92*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 4*x^2 + 97*x + 20, x^93 + 74*x^91 + 124*x^90 + 75*x^89 + 12*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 84*x^82 + 67*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 85*x^73 + 4*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 28*x^66 + 101*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 119*x^25 + 124*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 100*x^18 + 111*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 113*x^9 + 116*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 44*x^2 + 33*x + 92, x^93 + 74*x^91 + 80*x^90 + 83*x^89 + 64*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 48*x^82 + 123*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 109*x^73 + 64*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 16*x^66 + 13*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 31*x^25 + 64*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 112*x^18 + 7*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 41*x^9 + 64*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 80*x^2 + 41*x, x^93 + 74*x^91 + 52*x^90 + 27*x^89 + 116*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 60*x^82 + 115*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 69*x^73 + 124*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 20*x^66 + 117*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 7*x^25 + 4*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 108*x^18 + 95*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 33*x^9 + 12*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 68*x^2 + 113*x + 36, x^93 + 74*x^91 + 124*x^90 + 75*x^89 + 76*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 20*x^82 + 3*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 85*x^73 + 68*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 92*x^66 + 37*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 119*x^25 + 60*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 36*x^18 + 47*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 113*x^9 + 52*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 108*x^2 + 97*x + 92, x^93 + 74*x^91 + 116*x^90 + 107*x^89 + 4*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 60*x^82 + 99*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 53*x^73 + 44*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 20*x^66 + 69*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 23*x^25 + 84*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 108*x^18 + 15*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 81*x^9 + 124*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 68*x^2 + x + 52, x^93 + 74*x^91 + 36*x^90 + 59*x^89 + 4*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 12*x^82 + 83*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 37*x^73 + 44*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 4*x^66 + 21*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 39*x^25 + 84*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 124*x^18 + 63*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + x^9 + 124*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 116*x^2 + 17*x + 116, x^93 + 74*x^91 + 116*x^90 + 91*x^89 + 52*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 60*x^82 + 115*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 5*x^73 + 60*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 20*x^66 + 117*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 71*x^25 + 68*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 108*x^18 + 95*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 97*x^9 + 76*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 68*x^2 + 113*x + 36, x^93 + 74*x^91 + 32*x^90 + 83*x^89 + 80*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 102*x^83 + 96*x^82 + 59*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 109*x^73 + 112*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 114*x^67 + 32*x^66 + 77*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 31*x^25 + 16*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 30*x^19 + 96*x^18 + 71*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 41*x^9 + 48*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 106*x^3 + 32*x^2 + 105*x + 16, x^93 + 74*x^91 + 124*x^90 + 27*x^89 + 60*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 20*x^82 + 51*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 69*x^73 + 20*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 92*x^66 + 53*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 7*x^25 + 108*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 36*x^18 + 31*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 33*x^9 + 68*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 108*x^2 + 49*x + 12, x^93 + 74*x^91 + 68*x^90 + 91*x^89 + 68*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 44*x^82 + 115*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 5*x^73 + 108*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 100*x^66 + 117*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 71*x^25 + 20*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 28*x^18 + 95*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 97*x^9 + 60*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 84*x^2 + 113*x + 116, x^93 + 74*x^91 + 24*x^90 + 19*x^89 + 104*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 72*x^82 + 123*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 45*x^73 + 120*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 24*x^66 + 13*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 95*x^25 + 8*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 104*x^18 + 7*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 105*x^9 + 24*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 56*x^2 + 41*x + 8, x^93 + 74*x^91 + 124*x^90 + 27*x^89 + 28*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 84*x^82 + 115*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 69*x^73 + 52*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 28*x^66 + 117*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 7*x^25 + 76*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 100*x^18 + 95*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 33*x^9 + 100*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 44*x^2 + 113*x + 44, x^93 + 74*x^91 + 48*x^90 + 67*x^89 + 112*x^88 + 4*x^87 + 32*x^86 + x^85 + 32*x^84 + 38*x^83 + 16*x^82 + 75*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 61*x^73 + 80*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 48*x^66 + 125*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 79*x^25 + 48*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 80*x^18 + 23*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 57*x^9 + 16*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 112*x^2 + 89*x + 48, x^93 + 74*x^91 + 12*x^90 + 107*x^89 + 60*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 68*x^82 + 99*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 53*x^73 + 20*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 108*x^66 + 69*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 23*x^25 + 108*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 20*x^18 + 15*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 81*x^9 + 68*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 60*x^2 + x + 12, x^93 + 74*x^91 + 88*x^90 + 19*x^89 + 8*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 72*x^82 + 59*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 45*x^73 + 88*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 24*x^66 + 77*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 95*x^25 + 40*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 104*x^18 + 71*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 105*x^9 + 120*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 56*x^2 + 105*x + 104, x^93 + 74*x^91 + 64*x^90 + 99*x^89 + 64*x^88 + 4*x^87 + 65*x^85 + 38*x^83 + 64*x^82 + 43*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 29*x^73 + 64*x^72 + 52*x^71 + 71*x^69 + 50*x^67 + 64*x^66 + 29*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 111*x^25 + 64*x^24 + 52*x^23 + 101*x^21 + 94*x^19 + 64*x^18 + 119*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 4*x^7 + 91*x^5 + 42*x^3 + 64*x^2 + 121*x + 64, x^93 + 74*x^91 + 64*x^90 + 83*x^89 + 48*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 38*x^83 + 123*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 109*x^73 + 16*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 50*x^67 + 13*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 31*x^25 + 112*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 94*x^19 + 7*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 41*x^9 + 80*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 42*x^3 + 41*x + 48, x^93 + 74*x^91 + 16*x^90 + 19*x^89 + 96*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 48*x^82 + 123*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 45*x^73 + 32*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 16*x^66 + 13*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 95*x^25 + 96*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 112*x^18 + 7*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 105*x^9 + 32*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 80*x^2 + 41*x + 96, x^93 + 74*x^91 + 19*x^89 + 48*x^88 + 68*x^87 + 33*x^85 + 32*x^84 + 102*x^83 + 123*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 45*x^73 + 16*x^72 + 116*x^71 + 39*x^69 + 32*x^68 + 114*x^67 + 13*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 95*x^25 + 112*x^24 + 116*x^23 + 69*x^21 + 32*x^20 + 30*x^19 + 7*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 105*x^9 + 80*x^8 + 68*x^7 + 59*x^5 + 32*x^4 + 106*x^3 + 41*x + 112, x^93 + 74*x^91 + 68*x^90 + 75*x^89 + 20*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 44*x^82 + 3*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 85*x^73 + 92*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 100*x^66 + 37*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 119*x^25 + 36*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 28*x^18 + 47*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 113*x^9 + 108*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 84*x^2 + 97*x + 4, x^93 + 74*x^91 + 96*x^90 + 67*x^89 + 64*x^88 + 68*x^87 + 65*x^85 + 64*x^84 + 102*x^83 + 96*x^82 + 11*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 61*x^73 + 64*x^72 + 116*x^71 + 71*x^69 + 64*x^68 + 114*x^67 + 32*x^66 + 61*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 79*x^25 + 64*x^24 + 116*x^23 + 101*x^21 + 64*x^20 + 30*x^19 + 96*x^18 + 87*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 57*x^9 + 64*x^8 + 68*x^7 + 91*x^5 + 64*x^4 + 106*x^3 + 32*x^2 + 25*x, x^93 + 74*x^91 + 76*x^90 + 43*x^89 + 60*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 68*x^82 + 99*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 117*x^73 + 20*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 108*x^66 + 69*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 87*x^25 + 108*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 20*x^18 + 15*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 17*x^9 + 68*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 60*x^2 + x + 76, x^93 + 74*x^91 + 124*x^90 + 123*x^89 + 28*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 20*x^82 + 83*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 101*x^73 + 52*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 92*x^66 + 21*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 103*x^25 + 76*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 36*x^18 + 63*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 65*x^9 + 100*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 108*x^2 + 17*x + 108, x^93 + 74*x^91 + 112*x^90 + 3*x^89 + 48*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 16*x^82 + 75*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 125*x^73 + 16*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 48*x^66 + 125*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 15*x^25 + 112*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 80*x^18 + 23*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 121*x^9 + 80*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 112*x^2 + 89*x + 48, x^93 + 74*x^91 + 124*x^90 + 91*x^89 + 28*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 20*x^82 + 115*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 5*x^73 + 52*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 92*x^66 + 117*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 71*x^25 + 76*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 36*x^18 + 95*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 97*x^9 + 100*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 108*x^2 + 113*x + 108, x^93 + 74*x^91 + 40*x^90 + 99*x^89 + 104*x^88 + 68*x^87 + 112*x^86 + x^85 + 48*x^84 + 102*x^83 + 56*x^82 + 107*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 29*x^73 + 120*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 104*x^66 + 93*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 111*x^25 + 8*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 24*x^18 + 55*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 25*x^9 + 24*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 72*x^2 + 57*x + 72, x^93 + 74*x^91 + 83*x^89 + 48*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 38*x^83 + 64*x^82 + 123*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 109*x^73 + 16*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 50*x^67 + 64*x^66 + 13*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 31*x^25 + 112*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 94*x^19 + 64*x^18 + 7*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 41*x^9 + 80*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 42*x^3 + 64*x^2 + 41*x + 48, x^93 + 74*x^91 + 8*x^90 + 35*x^89 + 8*x^88 + 68*x^87 + 48*x^86 + x^85 + 112*x^84 + 102*x^83 + 88*x^82 + 43*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 93*x^73 + 88*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 72*x^66 + 29*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 47*x^25 + 40*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 56*x^18 + 119*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 89*x^9 + 120*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 40*x^2 + 121*x + 104, x^93 + 74*x^91 + 100*x^90 + 75*x^89 + 116*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 12*x^82 + 3*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 85*x^73 + 124*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 4*x^66 + 37*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 119*x^25 + 4*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 124*x^18 + 47*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 113*x^9 + 12*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 116*x^2 + 97*x + 100, x^93 + 74*x^91 + 28*x^90 + 107*x^89 + 44*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 52*x^82 + 35*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 53*x^73 + 100*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 60*x^66 + 5*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 23*x^25 + 28*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 68*x^18 + 79*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 81*x^9 + 84*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 76*x^2 + 65*x + 124, x^93 + 74*x^91 + 108*x^90 + 91*x^89 + 44*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 100*x^82 + 115*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 5*x^73 + 100*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 76*x^66 + 117*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 71*x^25 + 28*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 52*x^18 + 95*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 97*x^9 + 84*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 28*x^2 + 113*x + 60, x^93 + 74*x^91 + 67*x^89 + 96*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 102*x^83 + 64*x^82 + 11*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 61*x^73 + 32*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 114*x^67 + 64*x^66 + 61*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 79*x^25 + 96*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 30*x^19 + 64*x^18 + 87*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 57*x^9 + 32*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 106*x^3 + 64*x^2 + 25*x + 32, x^93 + 74*x^91 + 68*x^90 + 11*x^89 + 84*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 44*x^82 + 67*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 21*x^73 + 28*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 100*x^66 + 101*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 55*x^25 + 100*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 28*x^18 + 111*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 49*x^9 + 44*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 84*x^2 + 33*x + 68, x^93 + 74*x^91 + 56*x^90 + 35*x^89 + 24*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 40*x^82 + 107*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 93*x^73 + 8*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 56*x^66 + 93*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 47*x^25 + 120*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 72*x^18 + 55*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 89*x^9 + 104*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 88*x^2 + 57*x + 120, x^93 + 74*x^91 + 8*x^90 + 51*x^89 + 88*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 88*x^82 + 27*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 13*x^73 + 72*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 72*x^66 + 109*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 127*x^25 + 56*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 56*x^18 + 39*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 73*x^9 + 40*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 40*x^2 + 9*x + 120, x^93 + 74*x^91 + 115*x^89 + 48*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 38*x^83 + 64*x^82 + 91*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 77*x^73 + 16*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 50*x^67 + 64*x^66 + 45*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 63*x^25 + 112*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 94*x^19 + 64*x^18 + 103*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 9*x^9 + 80*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 42*x^3 + 64*x^2 + 73*x + 48, x^93 + 74*x^91 + 112*x^90 + 99*x^89 + 48*x^88 + 68*x^87 + 96*x^86 + x^85 + 96*x^84 + 102*x^83 + 16*x^82 + 107*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 29*x^73 + 16*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 48*x^66 + 93*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 111*x^25 + 112*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 80*x^18 + 55*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 25*x^9 + 80*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 112*x^2 + 57*x + 48, x^93 + 74*x^91 + 76*x^90 + 75*x^89 + 92*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 4*x^82 + 3*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 85*x^73 + 116*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 44*x^66 + 37*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 119*x^25 + 12*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 84*x^18 + 47*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 113*x^9 + 36*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 124*x^2 + 97*x + 44, x^93 + 74*x^91 + 32*x^90 + 67*x^89 + 96*x^88 + 4*x^87 + 64*x^86 + x^85 + 64*x^84 + 38*x^83 + 96*x^82 + 75*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 61*x^73 + 32*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 50*x^67 + 32*x^66 + 125*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 79*x^25 + 96*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 94*x^19 + 96*x^18 + 23*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 57*x^9 + 32*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 42*x^3 + 32*x^2 + 89*x + 96, x^93 + 74*x^91 + 84*x^90 + 11*x^89 + 36*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 28*x^82 + 3*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 21*x^73 + 12*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 52*x^66 + 37*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 55*x^25 + 116*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 76*x^18 + 47*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 49*x^9 + 92*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 100*x^2 + 97*x + 20, x^93 + 74*x^91 + 40*x^90 + 83*x^89 + 120*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 120*x^82 + 59*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 109*x^73 + 40*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 40*x^66 + 77*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 31*x^25 + 88*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 88*x^18 + 71*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 41*x^9 + 8*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 8*x^2 + 105*x + 88, x^93 + 74*x^91 + 8*x^90 + 99*x^89 + 104*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 24*x^82 + 43*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 29*x^73 + 120*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 8*x^66 + 29*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 111*x^25 + 8*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 120*x^18 + 119*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 25*x^9 + 24*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 104*x^2 + 121*x + 8, x^93 + 74*x^91 + 108*x^90 + 11*x^89 + 28*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 36*x^82 + 3*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 21*x^73 + 52*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 12*x^66 + 37*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 55*x^25 + 76*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 116*x^18 + 47*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 49*x^9 + 100*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 92*x^2 + 97*x + 44, x^93 + 74*x^91 + 16*x^90 + 51*x^89 + 32*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 38*x^83 + 112*x^82 + 27*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 13*x^73 + 96*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 50*x^67 + 80*x^66 + 109*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 127*x^25 + 32*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 94*x^19 + 48*x^18 + 39*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 73*x^9 + 96*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 42*x^3 + 16*x^2 + 9*x + 96, x^93 + 74*x^91 + 40*x^90 + 99*x^89 + 72*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 120*x^82 + 43*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 29*x^73 + 24*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 40*x^66 + 29*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 111*x^25 + 104*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 88*x^18 + 119*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 25*x^9 + 56*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 8*x^2 + 121*x + 104, x^93 + 74*x^91 + 84*x^90 + 123*x^89 + 20*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 92*x^82 + 83*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 101*x^73 + 92*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 116*x^66 + 21*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 103*x^25 + 36*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 12*x^18 + 63*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 65*x^9 + 108*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 36*x^2 + 17*x + 4, x^93 + 74*x^91 + 56*x^90 + 99*x^89 + 88*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 40*x^82 + 43*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 29*x^73 + 72*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 56*x^66 + 29*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 111*x^25 + 56*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 72*x^18 + 119*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 25*x^9 + 40*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 88*x^2 + 121*x + 56, x^93 + 74*x^91 + 64*x^90 + 83*x^89 + 112*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 38*x^83 + 123*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 109*x^73 + 80*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 50*x^67 + 13*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 31*x^25 + 48*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 94*x^19 + 7*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 41*x^9 + 16*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 42*x^3 + 41*x + 112, x^93 + 74*x^91 + 19*x^89 + 112*x^88 + 68*x^87 + 33*x^85 + 32*x^84 + 102*x^83 + 123*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 45*x^73 + 80*x^72 + 116*x^71 + 39*x^69 + 32*x^68 + 114*x^67 + 13*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 95*x^25 + 48*x^24 + 116*x^23 + 69*x^21 + 32*x^20 + 30*x^19 + 7*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 105*x^9 + 16*x^8 + 68*x^7 + 59*x^5 + 32*x^4 + 106*x^3 + 41*x + 48, x^93 + 74*x^91 + 112*x^90 + 51*x^89 + 68*x^87 + 32*x^86 + 97*x^85 + 102*x^83 + 80*x^82 + 91*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 13*x^73 + 116*x^71 + 32*x^70 + 103*x^69 + 114*x^67 + 112*x^66 + 45*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 127*x^25 + 116*x^23 + 32*x^22 + 5*x^21 + 30*x^19 + 16*x^18 + 103*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 73*x^9 + 68*x^7 + 32*x^6 + 123*x^5 + 106*x^3 + 48*x^2 + 73*x, x^93 + 74*x^91 + 108*x^90 + 11*x^89 + 124*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 100*x^82 + 67*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 21*x^73 + 84*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 76*x^66 + 101*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 55*x^25 + 44*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 52*x^18 + 111*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 49*x^9 + 4*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 28*x^2 + 33*x + 76, x^93 + 74*x^91 + 48*x^90 + 35*x^89 + 16*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 16*x^82 + 107*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 93*x^73 + 48*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 48*x^66 + 93*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 47*x^25 + 80*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 80*x^18 + 55*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 89*x^9 + 112*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 112*x^2 + 57*x + 80, x^93 + 74*x^91 + 116*x^90 + 91*x^89 + 20*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 60*x^82 + 115*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 5*x^73 + 92*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 20*x^66 + 117*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 71*x^25 + 36*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 108*x^18 + 95*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 97*x^9 + 108*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 68*x^2 + 113*x + 4, x^93 + 74*x^91 + 40*x^90 + 19*x^89 + 56*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 56*x^82 + 59*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 45*x^73 + 104*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 104*x^66 + 77*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 95*x^25 + 24*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 24*x^18 + 71*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 105*x^9 + 72*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 72*x^2 + 105*x + 88, x^93 + 74*x^91 + 68*x^90 + 123*x^89 + 36*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 108*x^82 + 19*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 101*x^73 + 12*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 36*x^66 + 85*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 103*x^25 + 116*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 92*x^18 + 127*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 65*x^9 + 92*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 20*x^2 + 81*x + 20, x^93 + 74*x^91 + 100*x^90 + 27*x^89 + 100*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 76*x^82 + 115*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 69*x^73 + 76*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 68*x^66 + 117*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 7*x^25 + 52*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 60*x^18 + 95*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 33*x^9 + 28*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 52*x^2 + 113*x + 84, x^93 + 74*x^91 + 32*x^90 + 99*x^89 + 64*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 38*x^83 + 96*x^82 + 43*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 29*x^73 + 64*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 50*x^67 + 32*x^66 + 29*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 111*x^25 + 64*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 94*x^19 + 96*x^18 + 119*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 25*x^9 + 64*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 42*x^3 + 32*x^2 + 121*x + 64, x^93 + 74*x^91 + 112*x^90 + 115*x^89 + 4*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 16*x^82 + 91*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 77*x^73 + 52*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 48*x^66 + 45*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 63*x^25 + 52*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 80*x^18 + 103*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 9*x^9 + 4*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 112*x^2 + 73*x + 64, x^93 + 74*x^91 + 92*x^90 + 75*x^89 + 76*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 116*x^82 + 67*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 85*x^73 + 68*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 124*x^66 + 101*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 119*x^25 + 60*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 4*x^18 + 111*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 113*x^9 + 52*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 12*x^2 + 33*x + 28, x^93 + 74*x^91 + 32*x^90 + 99*x^89 + 32*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 38*x^83 + 96*x^82 + 43*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 29*x^73 + 96*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 50*x^67 + 32*x^66 + 29*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 111*x^25 + 32*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 94*x^19 + 96*x^18 + 119*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 25*x^9 + 96*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 42*x^3 + 32*x^2 + 121*x + 32, x^93 + 74*x^91 + 80*x^90 + 115*x^89 + 64*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 48*x^82 + 91*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 77*x^73 + 64*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 16*x^66 + 45*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 63*x^25 + 64*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 112*x^18 + 103*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 9*x^9 + 64*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 80*x^2 + 73*x, x^93 + 74*x^91 + 4*x^90 + 91*x^89 + 100*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 108*x^82 + 115*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 5*x^73 + 76*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 36*x^66 + 117*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 71*x^25 + 52*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 92*x^18 + 95*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 97*x^9 + 28*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 20*x^2 + 113*x + 20, x^93 + 74*x^91 + 4*x^90 + 107*x^89 + 52*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 108*x^82 + 99*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 53*x^73 + 60*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 36*x^66 + 69*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 23*x^25 + 68*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 92*x^18 + 15*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 81*x^9 + 76*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 20*x^2 + x + 36, x^93 + 74*x^91 + 72*x^90 + 83*x^89 + 88*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 24*x^82 + 123*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 109*x^73 + 72*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 8*x^66 + 13*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 31*x^25 + 56*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 120*x^18 + 7*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 41*x^9 + 40*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 104*x^2 + 41*x + 120, x^93 + 74*x^91 + 60*x^90 + 91*x^89 + 60*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 20*x^82 + 51*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 5*x^73 + 20*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 92*x^66 + 53*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 71*x^25 + 108*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 36*x^18 + 31*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 97*x^9 + 68*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 108*x^2 + 49*x + 76, x^93 + 74*x^91 + 100*x^90 + 107*x^89 + 20*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 76*x^82 + 35*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 53*x^73 + 92*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 68*x^66 + 5*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 23*x^25 + 36*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 60*x^18 + 79*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 81*x^9 + 108*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 52*x^2 + 65*x + 68, x^93 + 74*x^91 + 120*x^90 + 35*x^89 + 24*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 104*x^82 + 107*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 93*x^73 + 8*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 120*x^66 + 93*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 47*x^25 + 120*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 8*x^18 + 55*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 89*x^9 + 104*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 24*x^2 + 57*x + 120, x^93 + 74*x^91 + 80*x^90 + 99*x^89 + 80*x^88 + 68*x^87 + 32*x^86 + x^85 + 32*x^84 + 102*x^83 + 48*x^82 + 107*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 29*x^73 + 112*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 16*x^66 + 93*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 111*x^25 + 16*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 112*x^18 + 55*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 25*x^9 + 48*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 80*x^2 + 57*x + 80, x^93 + 74*x^91 + 124*x^90 + 91*x^89 + 60*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 84*x^82 + 51*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 5*x^73 + 20*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 28*x^66 + 53*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 71*x^25 + 108*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 100*x^18 + 31*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 97*x^9 + 68*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 44*x^2 + 49*x + 76, x^93 + 74*x^91 + 8*x^90 + 19*x^89 + 24*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 24*x^82 + 123*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 45*x^73 + 8*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 8*x^66 + 13*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 95*x^25 + 120*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 120*x^18 + 7*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 105*x^9 + 104*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 104*x^2 + 41*x + 120, x^93 + 74*x^91 + 108*x^90 + 107*x^89 + 28*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 36*x^82 + 35*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 53*x^73 + 52*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 12*x^66 + 5*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 23*x^25 + 76*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 116*x^18 + 79*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 81*x^9 + 100*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 92*x^2 + 65*x + 44, x^93 + 74*x^91 + 51*x^89 + 80*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 38*x^83 + 64*x^82 + 27*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 13*x^73 + 112*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 50*x^67 + 64*x^66 + 109*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 127*x^25 + 16*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 94*x^19 + 64*x^18 + 39*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 73*x^9 + 48*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 42*x^3 + 64*x^2 + 9*x + 80, x^93 + 74*x^91 + 72*x^90 + 67*x^89 + 40*x^88 + 4*x^87 + 112*x^86 + x^85 + 112*x^84 + 38*x^83 + 88*x^82 + 75*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 61*x^73 + 56*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 72*x^66 + 125*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 79*x^25 + 72*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 56*x^18 + 23*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 57*x^9 + 88*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 40*x^2 + 89*x + 72, x^93 + 74*x^91 + 76*x^90 + 91*x^89 + 76*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 68*x^82 + 51*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 5*x^73 + 68*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 108*x^66 + 53*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 71*x^25 + 60*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 20*x^18 + 31*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 97*x^9 + 52*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 60*x^2 + 49*x + 28, x^93 + 74*x^91 + 76*x^90 + 107*x^89 + 60*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 4*x^82 + 99*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 53*x^73 + 20*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 44*x^66 + 69*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 23*x^25 + 108*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 84*x^18 + 15*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 81*x^9 + 68*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 124*x^2 + x + 12, x^93 + 74*x^91 + 64*x^90 + 115*x^89 + 48*x^88 + 68*x^87 + 97*x^85 + 32*x^84 + 102*x^83 + 64*x^82 + 27*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 77*x^73 + 16*x^72 + 116*x^71 + 103*x^69 + 32*x^68 + 114*x^67 + 64*x^66 + 109*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 63*x^25 + 112*x^24 + 116*x^23 + 5*x^21 + 32*x^20 + 30*x^19 + 64*x^18 + 39*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 9*x^9 + 80*x^8 + 68*x^7 + 123*x^5 + 32*x^4 + 106*x^3 + 64*x^2 + 9*x + 112, x^93 + 74*x^91 + 112*x^90 + 83*x^89 + 32*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 38*x^83 + 16*x^82 + 123*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 109*x^73 + 96*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 50*x^67 + 48*x^66 + 13*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 31*x^25 + 32*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 94*x^19 + 80*x^18 + 7*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 41*x^9 + 96*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 42*x^3 + 112*x^2 + 41*x + 96, x^93 + 74*x^91 + 92*x^90 + 27*x^89 + 92*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 52*x^82 + 51*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 69*x^73 + 116*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 60*x^66 + 53*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 7*x^25 + 12*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 68*x^18 + 31*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 33*x^9 + 36*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 76*x^2 + 49*x + 44, x^93 + 74*x^91 + 8*x^90 + 19*x^89 + 24*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 88*x^82 + 59*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 45*x^73 + 8*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 72*x^66 + 77*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 95*x^25 + 120*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 56*x^18 + 71*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 105*x^9 + 104*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 40*x^2 + 105*x + 56, x^93 + 74*x^91 + 68*x^90 + 107*x^89 + 116*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 44*x^82 + 99*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 53*x^73 + 124*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 100*x^66 + 69*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 23*x^25 + 4*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 28*x^18 + 15*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 81*x^9 + 12*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 84*x^2 + x + 100, x^93 + 74*x^91 + 44*x^90 + 107*x^89 + 124*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 100*x^82 + 35*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 53*x^73 + 84*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 76*x^66 + 5*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 23*x^25 + 44*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 52*x^18 + 79*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 81*x^9 + 4*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 28*x^2 + 65*x + 12, x^93 + 74*x^91 + 4*x^90 + 43*x^89 + 20*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 108*x^82 + 35*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 117*x^73 + 92*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 36*x^66 + 5*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 87*x^25 + 36*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 92*x^18 + 79*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 17*x^9 + 108*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 20*x^2 + 65*x + 4, x^93 + 74*x^91 + 12*x^90 + 107*x^89 + 124*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 68*x^82 + 99*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 53*x^73 + 84*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 108*x^66 + 69*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 23*x^25 + 44*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 20*x^18 + 15*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 81*x^9 + 4*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 60*x^2 + x + 76, x^93 + 74*x^91 + 72*x^90 + 3*x^89 + 72*x^88 + 4*x^87 + 112*x^86 + x^85 + 48*x^84 + 38*x^83 + 88*x^82 + 11*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 125*x^73 + 24*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 72*x^66 + 61*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 15*x^25 + 104*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 56*x^18 + 87*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 121*x^9 + 56*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 40*x^2 + 25*x + 104, x^93 + 74*x^91 + 3*x^89 + 64*x^88 + 4*x^87 + x^85 + 38*x^83 + 11*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 125*x^73 + 64*x^72 + 52*x^71 + 7*x^69 + 50*x^67 + 61*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 15*x^25 + 64*x^24 + 52*x^23 + 37*x^21 + 94*x^19 + 87*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 121*x^9 + 64*x^8 + 4*x^7 + 27*x^5 + 42*x^3 + 25*x + 64, x^93 + 74*x^91 + 20*x^90 + 107*x^89 + 4*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 92*x^82 + 35*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 53*x^73 + 44*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 116*x^66 + 5*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 23*x^25 + 84*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 12*x^18 + 79*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 81*x^9 + 124*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 36*x^2 + 65*x + 116, x^93 + 74*x^91 + 76*x^90 + 43*x^89 + 28*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 68*x^82 + 99*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 117*x^73 + 52*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 108*x^66 + 69*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 87*x^25 + 76*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 20*x^18 + 15*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 17*x^9 + 100*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 60*x^2 + x + 44, x^93 + 74*x^91 + 40*x^90 + 51*x^89 + 88*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 120*x^82 + 91*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 13*x^73 + 72*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 40*x^66 + 45*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 127*x^25 + 56*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 88*x^18 + 103*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 73*x^9 + 40*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 8*x^2 + 73*x + 56, x^93 + 74*x^91 + 36*x^90 + 59*x^89 + 100*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 12*x^82 + 83*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 37*x^73 + 76*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 4*x^66 + 21*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 39*x^25 + 52*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 124*x^18 + 63*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + x^9 + 28*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 116*x^2 + 17*x + 84, x^93 + 74*x^91 + 112*x^90 + 19*x^89 + 4*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 16*x^82 + 59*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 45*x^73 + 52*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 48*x^66 + 77*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 95*x^25 + 52*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 80*x^18 + 71*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 105*x^9 + 4*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 112*x^2 + 105*x + 64, x^93 + 74*x^91 + 56*x^90 + 99*x^89 + 120*x^88 + 68*x^87 + 80*x^86 + x^85 + 16*x^84 + 102*x^83 + 104*x^82 + 107*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 29*x^73 + 40*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 120*x^66 + 93*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 111*x^25 + 88*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 8*x^18 + 55*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 25*x^9 + 8*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 24*x^2 + 57*x + 24, x^93 + 74*x^91 + 124*x^90 + 75*x^89 + 108*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 20*x^82 + 3*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 85*x^73 + 36*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 92*x^66 + 37*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 119*x^25 + 92*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 36*x^18 + 47*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 113*x^9 + 20*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 108*x^2 + 97*x + 124, x^93 + 74*x^91 + 16*x^90 + 67*x^89 + 80*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 112*x^82 + 11*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 61*x^73 + 112*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 80*x^66 + 61*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 79*x^25 + 16*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 48*x^18 + 87*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 57*x^9 + 48*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 16*x^2 + 25*x + 80, x^93 + 74*x^91 + 44*x^90 + 123*x^89 + 44*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 36*x^82 + 83*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 101*x^73 + 100*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 12*x^66 + 21*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 103*x^25 + 28*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 116*x^18 + 63*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 65*x^9 + 84*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 92*x^2 + 17*x + 60, x^93 + 74*x^91 + 80*x^90 + 19*x^89 + 64*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 48*x^82 + 59*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 45*x^73 + 64*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 16*x^66 + 77*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 95*x^25 + 64*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 112*x^18 + 71*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 105*x^9 + 64*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 80*x^2 + 105*x, x^93 + 74*x^91 + 96*x^90 + 3*x^89 + 96*x^88 + 4*x^87 + 64*x^86 + x^85 + 64*x^84 + 38*x^83 + 32*x^82 + 11*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 125*x^73 + 32*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 50*x^67 + 96*x^66 + 61*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 15*x^25 + 96*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 94*x^19 + 32*x^18 + 87*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 121*x^9 + 32*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 42*x^3 + 96*x^2 + 25*x + 96, x^93 + 74*x^91 + 44*x^90 + 91*x^89 + 44*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 100*x^82 + 51*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 5*x^73 + 100*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 76*x^66 + 53*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 71*x^25 + 28*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 52*x^18 + 31*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 97*x^9 + 84*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 28*x^2 + 49*x + 124, x^93 + 74*x^91 + 104*x^90 + 35*x^89 + 104*x^88 + 68*x^87 + 112*x^86 + x^85 + 48*x^84 + 102*x^83 + 120*x^82 + 43*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 93*x^73 + 120*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 40*x^66 + 29*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 47*x^25 + 8*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 88*x^18 + 119*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 89*x^9 + 24*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 8*x^2 + 121*x + 72, x^93 + 74*x^91 + 104*x^90 + 99*x^89 + 8*x^88 + 68*x^87 + 112*x^86 + x^85 + 112*x^84 + 102*x^83 + 120*x^82 + 107*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 29*x^73 + 88*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 40*x^66 + 93*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 111*x^25 + 40*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 88*x^18 + 55*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 25*x^9 + 120*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 8*x^2 + 57*x + 104, x^93 + 74*x^91 + 8*x^90 + 19*x^89 + 120*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 88*x^82 + 59*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 45*x^73 + 40*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 72*x^66 + 77*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 95*x^25 + 88*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 56*x^18 + 71*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 105*x^9 + 8*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 40*x^2 + 105*x + 24, x^93 + 74*x^91 + 20*x^90 + 75*x^89 + 36*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 92*x^82 + 67*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 85*x^73 + 12*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 116*x^66 + 101*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 119*x^25 + 116*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 12*x^18 + 111*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 113*x^9 + 92*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 36*x^2 + 33*x + 20, x^93 + 74*x^91 + 64*x^90 + 51*x^89 + 16*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 38*x^83 + 27*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 13*x^73 + 48*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 50*x^67 + 109*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 127*x^25 + 80*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 94*x^19 + 39*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 73*x^9 + 112*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 42*x^3 + 9*x + 16, x^93 + 74*x^91 + 112*x^90 + 115*x^89 + 32*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 38*x^83 + 16*x^82 + 91*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 77*x^73 + 96*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 50*x^67 + 48*x^66 + 45*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 63*x^25 + 32*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 94*x^19 + 80*x^18 + 103*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 9*x^9 + 96*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 42*x^3 + 112*x^2 + 73*x + 96, x^93 + 74*x^91 + 44*x^90 + 91*x^89 + 108*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 100*x^82 + 51*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 5*x^73 + 36*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 76*x^66 + 53*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 71*x^25 + 92*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 52*x^18 + 31*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 97*x^9 + 20*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 28*x^2 + 49*x + 60, x^93 + 74*x^91 + 4*x^90 + 91*x^89 + 100*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 44*x^82 + 51*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 5*x^73 + 76*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 100*x^66 + 53*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 71*x^25 + 52*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 28*x^18 + 31*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 97*x^9 + 28*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 84*x^2 + 49*x + 84, x^93 + 74*x^91 + 60*x^90 + 123*x^89 + 60*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 20*x^82 + 19*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 101*x^73 + 20*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 92*x^66 + 85*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 103*x^25 + 108*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 36*x^18 + 127*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 65*x^9 + 68*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 108*x^2 + 81*x + 76, x^93 + 74*x^91 + 120*x^90 + 67*x^89 + 88*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 40*x^82 + 11*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 61*x^73 + 72*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 56*x^66 + 61*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 79*x^25 + 56*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 72*x^18 + 87*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 57*x^9 + 40*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 88*x^2 + 25*x + 120, x^93 + 74*x^91 + 3*x^89 + 32*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 102*x^83 + 64*x^82 + 75*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 125*x^73 + 96*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 114*x^67 + 64*x^66 + 125*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 15*x^25 + 32*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 30*x^19 + 64*x^18 + 23*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 121*x^9 + 96*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 106*x^3 + 64*x^2 + 89*x + 96, x^93 + 74*x^91 + 72*x^90 + 19*x^89 + 120*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 88*x^82 + 123*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 45*x^73 + 40*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 72*x^66 + 13*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 95*x^25 + 88*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 56*x^18 + 7*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 105*x^9 + 8*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 40*x^2 + 41*x + 88, x^93 + 74*x^91 + 96*x^90 + 83*x^89 + 112*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 102*x^83 + 32*x^82 + 59*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 109*x^73 + 80*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 114*x^67 + 96*x^66 + 77*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 31*x^25 + 48*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 30*x^19 + 32*x^18 + 71*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 41*x^9 + 16*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 106*x^3 + 96*x^2 + 105*x + 48, x^93 + 74*x^91 + 51*x^89 + 16*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 38*x^83 + 64*x^82 + 27*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 13*x^73 + 48*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 50*x^67 + 64*x^66 + 109*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 127*x^25 + 80*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 94*x^19 + 64*x^18 + 39*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 73*x^9 + 112*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 42*x^3 + 64*x^2 + 9*x + 16, x^93 + 74*x^91 + 80*x^90 + 99*x^89 + 112*x^88 + 68*x^87 + 32*x^86 + x^85 + 96*x^84 + 102*x^83 + 48*x^82 + 107*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 29*x^73 + 80*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 16*x^66 + 93*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 111*x^25 + 48*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 112*x^18 + 55*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 25*x^9 + 16*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 80*x^2 + 57*x + 112, x^93 + 74*x^91 + 104*x^90 + 99*x^89 + 104*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 56*x^82 + 43*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 29*x^73 + 120*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 104*x^66 + 29*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 111*x^25 + 8*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 24*x^18 + 119*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 25*x^9 + 24*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 72*x^2 + 121*x + 8, x^93 + 74*x^91 + 44*x^90 + 75*x^89 + 28*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 100*x^82 + 67*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 85*x^73 + 52*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 76*x^66 + 101*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 119*x^25 + 76*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 52*x^18 + 111*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 113*x^9 + 100*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 28*x^2 + 33*x + 44, x^93 + 74*x^91 + 19*x^89 + 80*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 38*x^83 + 64*x^82 + 59*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 45*x^73 + 112*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 50*x^67 + 64*x^66 + 77*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 95*x^25 + 16*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 94*x^19 + 64*x^18 + 71*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 105*x^9 + 48*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 42*x^3 + 64*x^2 + 105*x + 80, x^93 + 74*x^91 + 112*x^90 + 67*x^89 + 80*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 16*x^82 + 11*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 61*x^73 + 112*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 48*x^66 + 61*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 79*x^25 + 16*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 80*x^18 + 87*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 57*x^9 + 48*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 112*x^2 + 25*x + 80, x^93 + 74*x^91 + 44*x^90 + 75*x^89 + 28*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 36*x^82 + 3*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 85*x^73 + 52*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 12*x^66 + 37*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 119*x^25 + 76*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 116*x^18 + 47*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 113*x^9 + 100*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 92*x^2 + 97*x + 108, x^93 + 74*x^91 + 76*x^90 + 91*x^89 + 12*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 4*x^82 + 115*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 5*x^73 + 4*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 44*x^66 + 117*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 71*x^25 + 124*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 84*x^18 + 95*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 97*x^9 + 116*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 124*x^2 + 113*x + 28, x^93 + 74*x^91 + 8*x^90 + 99*x^89 + 8*x^88 + 68*x^87 + 48*x^86 + x^85 + 112*x^84 + 102*x^83 + 88*x^82 + 107*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 29*x^73 + 88*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 72*x^66 + 93*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 111*x^25 + 40*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 56*x^18 + 55*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 25*x^9 + 120*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 40*x^2 + 57*x + 104, x^93 + 74*x^91 + 4*x^90 + 107*x^89 + 20*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 108*x^82 + 99*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 53*x^73 + 92*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 36*x^66 + 69*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 23*x^25 + 36*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 92*x^18 + 15*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 81*x^9 + 108*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 20*x^2 + x + 4, x^93 + 74*x^91 + 24*x^90 + 67*x^89 + 56*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 8*x^82 + 11*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 61*x^73 + 104*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 88*x^66 + 61*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 79*x^25 + 24*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 40*x^18 + 87*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 57*x^9 + 72*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 120*x^2 + 25*x + 88, x^93 + 74*x^91 + 100*x^90 + 75*x^89 + 52*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 12*x^82 + 3*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 85*x^73 + 60*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 4*x^66 + 37*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 119*x^25 + 68*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 124*x^18 + 47*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 113*x^9 + 76*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 116*x^2 + 97*x + 36, x^93 + 74*x^91 + 80*x^90 + 115*x^89 + 68*x^87 + 96*x^86 + 97*x^85 + 102*x^83 + 112*x^82 + 27*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 77*x^73 + 116*x^71 + 96*x^70 + 103*x^69 + 114*x^67 + 80*x^66 + 109*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 63*x^25 + 116*x^23 + 96*x^22 + 5*x^21 + 30*x^19 + 48*x^18 + 39*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 9*x^9 + 68*x^7 + 96*x^6 + 123*x^5 + 106*x^3 + 16*x^2 + 9*x, x^93 + 74*x^91 + 104*x^90 + 51*x^89 + 120*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 56*x^82 + 91*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 13*x^73 + 40*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 104*x^66 + 45*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 127*x^25 + 88*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 24*x^18 + 103*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 73*x^9 + 8*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 72*x^2 + 73*x + 88, x^93 + 74*x^91 + 108*x^90 + 43*x^89 + 60*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 100*x^82 + 35*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 117*x^73 + 20*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 76*x^66 + 5*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 87*x^25 + 108*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 52*x^18 + 79*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 17*x^9 + 68*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 28*x^2 + 65*x + 12, x^93 + 74*x^91 + 56*x^90 + 35*x^89 + 56*x^88 + 68*x^87 + 80*x^86 + x^85 + 16*x^84 + 102*x^83 + 104*x^82 + 43*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 93*x^73 + 104*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 120*x^66 + 29*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 47*x^25 + 24*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 8*x^18 + 119*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 89*x^9 + 72*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 24*x^2 + 121*x + 88, x^93 + 74*x^91 + 100*x^90 + 123*x^89 + 36*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 12*x^82 + 83*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 101*x^73 + 12*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 4*x^66 + 21*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 103*x^25 + 116*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 124*x^18 + 63*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 65*x^9 + 92*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 116*x^2 + 17*x + 84, x^93 + 74*x^91 + 92*x^90 + 91*x^89 + 124*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 52*x^82 + 115*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 5*x^73 + 84*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 60*x^66 + 117*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 71*x^25 + 44*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 68*x^18 + 95*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 97*x^9 + 4*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 76*x^2 + 113*x + 76, x^93 + 74*x^91 + 104*x^90 + 3*x^89 + 72*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 120*x^82 + 75*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 125*x^73 + 24*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 40*x^66 + 125*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 15*x^25 + 104*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 88*x^18 + 23*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 121*x^9 + 56*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 8*x^2 + 89*x + 40, x^93 + 74*x^91 + 40*x^90 + 3*x^89 + 8*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 56*x^82 + 75*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 125*x^73 + 88*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 104*x^66 + 125*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 15*x^25 + 40*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 24*x^18 + 23*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 121*x^9 + 120*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 72*x^2 + 89*x + 104, x^93 + 74*x^91 + 108*x^90 + 59*x^89 + 44*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 36*x^82 + 83*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 37*x^73 + 100*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 12*x^66 + 21*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 39*x^25 + 28*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 116*x^18 + 63*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + x^9 + 84*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 92*x^2 + 17*x + 124, x^93 + 74*x^91 + 80*x^90 + 67*x^89 + 16*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 48*x^82 + 11*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 61*x^73 + 48*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 16*x^66 + 61*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 79*x^25 + 80*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 112*x^18 + 87*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 57*x^9 + 112*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 80*x^2 + 25*x + 16, x^93 + 74*x^91 + 60*x^90 + 11*x^89 + 76*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 84*x^82 + 67*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 21*x^73 + 68*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 28*x^66 + 101*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 55*x^25 + 60*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 100*x^18 + 111*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 49*x^9 + 52*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 44*x^2 + 33*x + 92, x^93 + 74*x^91 + 120*x^90 + 3*x^89 + 120*x^88 + 4*x^87 + 16*x^86 + x^85 + 80*x^84 + 38*x^83 + 104*x^82 + 11*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 125*x^73 + 40*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 120*x^66 + 61*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 15*x^25 + 88*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 8*x^18 + 87*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 121*x^9 + 8*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 24*x^2 + 25*x + 88, x^93 + 74*x^91 + 36*x^90 + 75*x^89 + 116*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 12*x^82 + 67*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 85*x^73 + 124*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 4*x^66 + 101*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 119*x^25 + 4*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 124*x^18 + 111*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 113*x^9 + 12*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 116*x^2 + 33*x + 36, x^93 + 74*x^91 + 76*x^90 + 59*x^89 + 12*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 68*x^82 + 83*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 37*x^73 + 4*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 108*x^66 + 21*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 39*x^25 + 124*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 20*x^18 + 63*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + x^9 + 116*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 60*x^2 + 17*x + 92, x^93 + 74*x^91 + 84*x^90 + 59*x^89 + 84*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 28*x^82 + 83*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 37*x^73 + 28*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 52*x^66 + 21*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 39*x^25 + 100*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 76*x^18 + 63*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + x^9 + 44*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 100*x^2 + 17*x + 4, x^93 + 74*x^91 + 108*x^90 + 27*x^89 + 76*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 100*x^82 + 51*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 69*x^73 + 68*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 76*x^66 + 53*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 7*x^25 + 60*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 52*x^18 + 31*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 33*x^9 + 52*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 28*x^2 + 49*x + 92, x^93 + 74*x^91 + 12*x^90 + 43*x^89 + 28*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 68*x^82 + 35*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 117*x^73 + 52*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 108*x^66 + 5*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 87*x^25 + 76*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 20*x^18 + 79*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 17*x^9 + 100*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 60*x^2 + 65*x + 108, x^93 + 74*x^91 + 88*x^90 + 35*x^89 + 24*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 8*x^82 + 107*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 93*x^73 + 8*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 88*x^66 + 93*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 47*x^25 + 120*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 40*x^18 + 55*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 89*x^9 + 104*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 120*x^2 + 57*x + 120, x^93 + 74*x^91 + 60*x^90 + 91*x^89 + 28*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 20*x^82 + 51*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 5*x^73 + 52*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 92*x^66 + 53*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 71*x^25 + 76*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 36*x^18 + 31*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 97*x^9 + 100*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 108*x^2 + 49*x + 44, x^93 + 74*x^91 + 28*x^90 + 27*x^89 + 60*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 52*x^82 + 115*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 69*x^73 + 20*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 60*x^66 + 117*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 7*x^25 + 108*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 68*x^18 + 95*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 33*x^9 + 68*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 76*x^2 + 113*x + 76, x^93 + 74*x^91 + 40*x^90 + 35*x^89 + 40*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 120*x^82 + 107*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 93*x^73 + 56*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 40*x^66 + 93*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 47*x^25 + 72*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 88*x^18 + 55*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 89*x^9 + 88*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 8*x^2 + 57*x + 72, x^93 + 74*x^91 + 36*x^90 + 91*x^89 + 68*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 12*x^82 + 51*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 5*x^73 + 108*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 4*x^66 + 53*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 71*x^25 + 20*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 124*x^18 + 31*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 97*x^9 + 60*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 116*x^2 + 49*x + 52, x^93 + 74*x^91 + 96*x^90 + 35*x^89 + 32*x^88 + 68*x^87 + x^85 + 102*x^83 + 96*x^82 + 43*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 93*x^73 + 96*x^72 + 116*x^71 + 7*x^69 + 114*x^67 + 32*x^66 + 29*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 47*x^25 + 32*x^24 + 116*x^23 + 37*x^21 + 30*x^19 + 96*x^18 + 119*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 68*x^7 + 27*x^5 + 106*x^3 + 32*x^2 + 121*x + 96, x^93 + 74*x^91 + 84*x^90 + 11*x^89 + 100*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 92*x^82 + 67*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 21*x^73 + 76*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 116*x^66 + 101*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 55*x^25 + 52*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 12*x^18 + 111*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 49*x^9 + 28*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 36*x^2 + 33*x + 20, x^93 + 74*x^91 + 56*x^90 + 67*x^89 + 120*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 104*x^82 + 11*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 61*x^73 + 40*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 120*x^66 + 61*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 79*x^25 + 88*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 8*x^18 + 87*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 57*x^9 + 8*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 24*x^2 + 25*x + 24, x^93 + 74*x^91 + 104*x^90 + 99*x^89 + 40*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 56*x^82 + 43*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 29*x^73 + 56*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 104*x^66 + 29*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 111*x^25 + 72*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 24*x^18 + 119*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 25*x^9 + 88*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 72*x^2 + 121*x + 72, x^93 + 74*x^91 + 108*x^90 + 43*x^89 + 124*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 100*x^82 + 35*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 117*x^73 + 84*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 76*x^66 + 5*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 87*x^25 + 44*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 52*x^18 + 79*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 17*x^9 + 4*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 28*x^2 + 65*x + 76, x^93 + 74*x^91 + 48*x^90 + 51*x^89 + 32*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 16*x^82 + 91*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 13*x^73 + 96*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 48*x^66 + 45*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 127*x^25 + 32*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 80*x^18 + 103*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 73*x^9 + 96*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 112*x^2 + 73*x + 32, x^93 + 74*x^91 + 92*x^90 + 75*x^89 + 44*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 116*x^82 + 67*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 85*x^73 + 100*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 124*x^66 + 101*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 119*x^25 + 28*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 4*x^18 + 111*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 113*x^9 + 84*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 12*x^2 + 33*x + 124, x^93 + 74*x^91 + 120*x^90 + 83*x^89 + 72*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 40*x^82 + 123*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 109*x^73 + 24*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 56*x^66 + 13*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 31*x^25 + 104*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 72*x^18 + 7*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 41*x^9 + 56*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 88*x^2 + 41*x + 40, x^93 + 74*x^91 + 96*x^90 + 35*x^89 + 96*x^88 + 68*x^87 + x^85 + 102*x^83 + 96*x^82 + 43*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 93*x^73 + 32*x^72 + 116*x^71 + 7*x^69 + 114*x^67 + 32*x^66 + 29*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 47*x^25 + 96*x^24 + 116*x^23 + 37*x^21 + 30*x^19 + 96*x^18 + 119*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 89*x^9 + 32*x^8 + 68*x^7 + 27*x^5 + 106*x^3 + 32*x^2 + 121*x + 32, x^93 + 74*x^91 + 52*x^90 + 59*x^89 + 20*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 124*x^82 + 19*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 37*x^73 + 92*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 84*x^66 + 85*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 39*x^25 + 36*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 44*x^18 + 127*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + x^9 + 108*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 4*x^2 + 81*x + 4, x^93 + 74*x^91 + 68*x^90 + 43*x^89 + 20*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 108*x^82 + 99*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 117*x^73 + 92*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 36*x^66 + 69*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 87*x^25 + 36*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 92*x^18 + 15*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 17*x^9 + 108*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 20*x^2 + x + 68, x^93 + 74*x^91 + 36*x^90 + 11*x^89 + 20*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 76*x^82 + 67*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 21*x^73 + 92*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 68*x^66 + 101*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 55*x^25 + 36*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 60*x^18 + 111*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 49*x^9 + 108*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 52*x^2 + 33*x + 4, x^93 + 74*x^91 + 124*x^90 + 123*x^89 + 28*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 84*x^82 + 19*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 101*x^73 + 52*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 28*x^66 + 85*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 103*x^25 + 76*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 100*x^18 + 127*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 65*x^9 + 100*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 44*x^2 + 81*x + 44, x^93 + 74*x^91 + 48*x^90 + 35*x^89 + 48*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 16*x^82 + 107*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 93*x^73 + 16*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 48*x^66 + 93*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 47*x^25 + 112*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 80*x^18 + 55*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 89*x^9 + 80*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 112*x^2 + 57*x + 112, x^93 + 74*x^91 + 20*x^90 + 43*x^89 + 68*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 28*x^82 + 35*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 117*x^73 + 108*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 52*x^66 + 5*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 87*x^25 + 20*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 76*x^18 + 79*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 17*x^9 + 60*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 100*x^2 + 65*x + 116, x^93 + 74*x^91 + 124*x^90 + 27*x^89 + 28*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 20*x^82 + 51*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 69*x^73 + 52*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 92*x^66 + 53*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 7*x^25 + 76*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 36*x^18 + 31*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 33*x^9 + 100*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 108*x^2 + 49*x + 108, x^93 + 74*x^91 + 36*x^90 + 75*x^89 + 84*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 76*x^82 + 3*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 85*x^73 + 28*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 68*x^66 + 37*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 119*x^25 + 100*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 60*x^18 + 47*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 113*x^9 + 44*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 52*x^2 + 97*x + 68, x^93 + 74*x^91 + 76*x^90 + 59*x^89 + 76*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 4*x^82 + 19*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 37*x^73 + 68*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 44*x^66 + 85*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 39*x^25 + 60*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 84*x^18 + 127*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + x^9 + 52*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 124*x^2 + 81*x + 92, x^93 + 74*x^91 + 80*x^90 + 99*x^89 + 16*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 112*x^82 + 43*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 29*x^73 + 48*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 80*x^66 + 29*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 111*x^25 + 80*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 48*x^18 + 119*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 25*x^9 + 112*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 16*x^2 + 121*x + 80, x^93 + 74*x^91 + 112*x^90 + 51*x^89 + 4*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 16*x^82 + 27*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 13*x^73 + 52*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 48*x^66 + 109*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 127*x^25 + 52*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 80*x^18 + 39*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 73*x^9 + 4*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 112*x^2 + 9*x + 64, x^93 + 74*x^91 + 64*x^90 + 19*x^89 + 16*x^88 + 68*x^87 + 33*x^85 + 96*x^84 + 102*x^83 + 64*x^82 + 123*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 45*x^73 + 48*x^72 + 116*x^71 + 39*x^69 + 96*x^68 + 114*x^67 + 64*x^66 + 13*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 95*x^25 + 80*x^24 + 116*x^23 + 69*x^21 + 96*x^20 + 30*x^19 + 64*x^18 + 7*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 105*x^9 + 112*x^8 + 68*x^7 + 59*x^5 + 96*x^4 + 106*x^3 + 64*x^2 + 41*x + 80, x^93 + 74*x^91 + 88*x^90 + 67*x^89 + 88*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 72*x^82 + 11*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 61*x^73 + 72*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 24*x^66 + 61*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 79*x^25 + 56*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 104*x^18 + 87*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 57*x^9 + 40*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 56*x^2 + 25*x + 120, x^93 + 74*x^91 + 116*x^90 + 43*x^89 + 36*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 60*x^82 + 35*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 117*x^73 + 12*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 20*x^66 + 5*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 87*x^25 + 116*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 108*x^18 + 79*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 17*x^9 + 92*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 68*x^2 + 65*x + 84, x^93 + 74*x^91 + 12*x^90 + 107*x^89 + 28*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 68*x^82 + 99*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 53*x^73 + 52*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 108*x^66 + 69*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 23*x^25 + 76*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 20*x^18 + 15*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 81*x^9 + 100*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 60*x^2 + x + 108, x^93 + 74*x^91 + 100*x^90 + 75*x^89 + 20*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 12*x^82 + 3*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 85*x^73 + 92*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 4*x^66 + 37*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 119*x^25 + 36*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 124*x^18 + 47*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 113*x^9 + 108*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 116*x^2 + 97*x + 4, x^93 + 74*x^91 + 48*x^90 + 51*x^89 + 32*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 38*x^83 + 80*x^82 + 27*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 13*x^73 + 96*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 50*x^67 + 112*x^66 + 109*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 127*x^25 + 32*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 94*x^19 + 16*x^18 + 39*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 73*x^9 + 96*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 42*x^3 + 48*x^2 + 9*x + 96, x^93 + 74*x^91 + 20*x^90 + 107*x^89 + 100*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 28*x^82 + 99*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 53*x^73 + 76*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 52*x^66 + 69*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 23*x^25 + 52*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 76*x^18 + 15*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 81*x^9 + 28*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 100*x^2 + x + 20, x^93 + 74*x^91 + 120*x^90 + 35*x^89 + 88*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 104*x^82 + 107*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 93*x^73 + 72*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 120*x^66 + 93*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 47*x^25 + 56*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 8*x^18 + 55*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 89*x^9 + 40*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 24*x^2 + 57*x + 56, x^93 + 74*x^91 + 8*x^90 + 67*x^89 + 104*x^88 + 4*x^87 + 112*x^86 + x^85 + 112*x^84 + 38*x^83 + 24*x^82 + 75*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 61*x^73 + 120*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 8*x^66 + 125*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 79*x^25 + 8*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 120*x^18 + 23*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 57*x^9 + 24*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 104*x^2 + 89*x + 8, x^93 + 74*x^91 + 16*x^90 + 51*x^89 + 96*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 48*x^82 + 91*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 13*x^73 + 32*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 16*x^66 + 45*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 127*x^25 + 96*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 112*x^18 + 103*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 73*x^9 + 32*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 80*x^2 + 73*x + 96, x^93 + 74*x^91 + 84*x^90 + 75*x^89 + 4*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 28*x^82 + 67*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 85*x^73 + 44*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 52*x^66 + 101*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 119*x^25 + 84*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 76*x^18 + 111*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 113*x^9 + 124*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 100*x^2 + 33*x + 116, x^93 + 74*x^91 + 124*x^90 + 107*x^89 + 44*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 84*x^82 + 35*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 53*x^73 + 100*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 28*x^66 + 5*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 23*x^25 + 28*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 100*x^18 + 79*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 81*x^9 + 84*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 44*x^2 + 65*x + 124, x^93 + 74*x^91 + 120*x^90 + 115*x^89 + 40*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 104*x^82 + 27*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 77*x^73 + 56*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 120*x^66 + 109*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 63*x^25 + 72*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 8*x^18 + 39*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 9*x^9 + 88*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 24*x^2 + 9*x + 72, x^93 + 74*x^91 + 68*x^90 + 59*x^89 + 68*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 44*x^82 + 19*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 37*x^73 + 108*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 100*x^66 + 85*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 39*x^25 + 20*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 28*x^18 + 127*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + x^9 + 60*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 84*x^2 + 81*x + 116, x^93 + 74*x^91 + 24*x^90 + 19*x^89 + 8*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 8*x^82 + 59*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 45*x^73 + 88*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 88*x^66 + 77*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 95*x^25 + 40*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 40*x^18 + 71*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 105*x^9 + 120*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 120*x^2 + 105*x + 104, x^93 + 74*x^91 + 84*x^90 + 43*x^89 + 4*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 28*x^82 + 99*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 117*x^73 + 44*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 52*x^66 + 69*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 87*x^25 + 84*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 76*x^18 + 15*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 17*x^9 + 124*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 100*x^2 + x + 116, x^93 + 74*x^91 + 76*x^90 + 91*x^89 + 44*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 68*x^82 + 51*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 5*x^73 + 100*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 108*x^66 + 53*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 71*x^25 + 28*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 20*x^18 + 31*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 97*x^9 + 84*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 60*x^2 + 49*x + 124, x^93 + 74*x^91 + 48*x^90 + 51*x^89 + 64*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 102*x^83 + 16*x^82 + 91*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 13*x^73 + 64*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 114*x^67 + 48*x^66 + 45*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 127*x^25 + 64*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 30*x^19 + 80*x^18 + 103*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 73*x^9 + 64*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 106*x^3 + 112*x^2 + 73*x + 64, x^93 + 74*x^91 + 104*x^90 + 35*x^89 + 72*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 56*x^82 + 107*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 93*x^73 + 24*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 104*x^66 + 93*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 47*x^25 + 104*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 24*x^18 + 55*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 89*x^9 + 56*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 72*x^2 + 57*x + 104, x^93 + 74*x^91 + 96*x^90 + 67*x^89 + 96*x^88 + 68*x^87 + 65*x^85 + 102*x^83 + 96*x^82 + 11*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 61*x^73 + 32*x^72 + 116*x^71 + 71*x^69 + 114*x^67 + 32*x^66 + 61*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 79*x^25 + 96*x^24 + 116*x^23 + 101*x^21 + 30*x^19 + 96*x^18 + 87*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 57*x^9 + 32*x^8 + 68*x^7 + 91*x^5 + 106*x^3 + 32*x^2 + 25*x + 32, x^93 + 74*x^91 + 52*x^90 + 27*x^89 + 20*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 60*x^82 + 115*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 69*x^73 + 92*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 20*x^66 + 117*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 7*x^25 + 36*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 108*x^18 + 95*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 33*x^9 + 108*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 68*x^2 + 113*x + 68, x^93 + 74*x^91 + 64*x^90 + 51*x^89 + 48*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 38*x^83 + 27*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 13*x^73 + 16*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 50*x^67 + 109*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 127*x^25 + 112*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 94*x^19 + 39*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 73*x^9 + 80*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 42*x^3 + 9*x + 48, x^93 + 74*x^91 + 83*x^89 + 48*x^88 + 68*x^87 + 33*x^85 + 32*x^84 + 102*x^83 + 59*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 109*x^73 + 16*x^72 + 116*x^71 + 39*x^69 + 32*x^68 + 114*x^67 + 77*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 31*x^25 + 112*x^24 + 116*x^23 + 69*x^21 + 32*x^20 + 30*x^19 + 71*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 41*x^9 + 80*x^8 + 68*x^7 + 59*x^5 + 32*x^4 + 106*x^3 + 105*x + 112, x^93 + 74*x^91 + 68*x^90 + 107*x^89 + 52*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 44*x^82 + 99*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 53*x^73 + 60*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 100*x^66 + 69*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 23*x^25 + 68*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 28*x^18 + 15*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 81*x^9 + 76*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 84*x^2 + x + 36, x^93 + 74*x^91 + 72*x^90 + 83*x^89 + 56*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 88*x^82 + 59*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 109*x^73 + 104*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 72*x^66 + 77*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 31*x^25 + 24*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 56*x^18 + 71*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 41*x^9 + 72*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 40*x^2 + 105*x + 24, x^93 + 74*x^91 + 92*x^90 + 123*x^89 + 28*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 52*x^82 + 83*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 101*x^73 + 52*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 60*x^66 + 21*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 103*x^25 + 76*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 68*x^18 + 63*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 65*x^9 + 100*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 76*x^2 + 17*x + 108, x^93 + 74*x^91 + 16*x^90 + 3*x^89 + 16*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 112*x^82 + 75*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 125*x^73 + 48*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 80*x^66 + 125*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 15*x^25 + 80*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 48*x^18 + 23*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 121*x^9 + 112*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 16*x^2 + 89*x + 16, x^93 + 74*x^91 + 32*x^90 + 115*x^89 + 48*x^88 + 4*x^87 + 33*x^85 + 96*x^84 + 38*x^83 + 32*x^82 + 91*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 77*x^73 + 16*x^72 + 52*x^71 + 39*x^69 + 96*x^68 + 50*x^67 + 96*x^66 + 45*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 63*x^25 + 112*x^24 + 52*x^23 + 69*x^21 + 96*x^20 + 94*x^19 + 32*x^18 + 103*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 9*x^9 + 80*x^8 + 4*x^7 + 59*x^5 + 96*x^4 + 42*x^3 + 96*x^2 + 73*x + 48, x^93 + 74*x^91 + 72*x^90 + 115*x^89 + 88*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 24*x^82 + 91*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 77*x^73 + 72*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 8*x^66 + 45*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 63*x^25 + 56*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 120*x^18 + 103*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 9*x^9 + 40*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 104*x^2 + 73*x + 120, x^93 + 74*x^91 + 84*x^90 + 43*x^89 + 68*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 28*x^82 + 99*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 117*x^73 + 108*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 52*x^66 + 69*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 87*x^25 + 20*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 76*x^18 + 15*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 17*x^9 + 60*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 100*x^2 + x + 52, x^93 + 74*x^91 + 96*x^90 + 67*x^89 + 64*x^88 + 4*x^87 + 64*x^86 + x^85 + 38*x^83 + 32*x^82 + 75*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 61*x^73 + 64*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 50*x^67 + 96*x^66 + 125*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 79*x^25 + 64*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 94*x^19 + 32*x^18 + 23*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 57*x^9 + 64*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 42*x^3 + 96*x^2 + 89*x + 64, x^93 + 74*x^91 + 72*x^90 + 35*x^89 + 40*x^88 + 68*x^87 + 48*x^86 + x^85 + 48*x^84 + 102*x^83 + 24*x^82 + 43*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 93*x^73 + 56*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 8*x^66 + 29*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 47*x^25 + 72*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 120*x^18 + 119*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 89*x^9 + 88*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 104*x^2 + 121*x + 8, x^93 + 74*x^91 + 116*x^90 + 27*x^89 + 20*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 60*x^82 + 51*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 69*x^73 + 92*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 20*x^66 + 53*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 7*x^25 + 36*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 108*x^18 + 31*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 33*x^9 + 108*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 68*x^2 + 49*x + 4, x^93 + 74*x^91 + 104*x^90 + 99*x^89 + 104*x^88 + 68*x^87 + 112*x^86 + x^85 + 48*x^84 + 102*x^83 + 120*x^82 + 107*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 29*x^73 + 120*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 40*x^66 + 93*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 111*x^25 + 8*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 88*x^18 + 55*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 25*x^9 + 24*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 8*x^2 + 57*x + 72, x^93 + 74*x^91 + 40*x^90 + 99*x^89 + 8*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 120*x^82 + 43*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 29*x^73 + 88*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 40*x^66 + 29*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 111*x^25 + 40*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 88*x^18 + 119*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 25*x^9 + 120*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 8*x^2 + 121*x + 40, x^93 + 74*x^91 + 60*x^90 + 107*x^89 + 76*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 84*x^82 + 99*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 53*x^73 + 68*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 28*x^66 + 69*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 23*x^25 + 60*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 100*x^18 + 15*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 81*x^9 + 52*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 44*x^2 + x + 92, x^93 + 74*x^91 + 16*x^90 + 99*x^89 + 80*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 48*x^82 + 43*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 29*x^73 + 112*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 16*x^66 + 29*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 111*x^25 + 16*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 112*x^18 + 119*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 25*x^9 + 48*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 80*x^2 + 121*x + 16, x^93 + 74*x^91 + 92*x^90 + 107*x^89 + 12*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 116*x^82 + 35*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 53*x^73 + 4*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 124*x^66 + 5*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 23*x^25 + 124*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 4*x^18 + 79*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 81*x^9 + 116*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 12*x^2 + 65*x + 92, x^93 + 74*x^91 + 96*x^90 + 67*x^89 + 32*x^88 + 4*x^87 + 64*x^86 + x^85 + 64*x^84 + 38*x^83 + 32*x^82 + 75*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 61*x^73 + 96*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 50*x^67 + 96*x^66 + 125*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 79*x^25 + 32*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 94*x^19 + 32*x^18 + 23*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 57*x^9 + 96*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 42*x^3 + 96*x^2 + 89*x + 32, x^93 + 74*x^91 + 116*x^90 + 107*x^89 + 36*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 60*x^82 + 99*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 53*x^73 + 12*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 20*x^66 + 69*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 23*x^25 + 116*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 108*x^18 + 15*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 81*x^9 + 92*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 68*x^2 + x + 84, x^93 + 74*x^91 + 32*x^90 + 3*x^89 + 4*x^87 + 64*x^86 + x^85 + 38*x^83 + 96*x^82 + 11*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 125*x^73 + 52*x^71 + 64*x^70 + 7*x^69 + 50*x^67 + 32*x^66 + 61*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 15*x^25 + 52*x^23 + 64*x^22 + 37*x^21 + 94*x^19 + 96*x^18 + 87*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 121*x^9 + 4*x^7 + 64*x^6 + 27*x^5 + 42*x^3 + 32*x^2 + 25*x, x^93 + 74*x^91 + 88*x^90 + 35*x^89 + 120*x^88 + 68*x^87 + 16*x^86 + x^85 + 16*x^84 + 102*x^83 + 72*x^82 + 43*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 93*x^73 + 40*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 24*x^66 + 29*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 47*x^25 + 88*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 104*x^18 + 119*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 89*x^9 + 8*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 56*x^2 + 121*x + 24, x^93 + 74*x^91 + 64*x^90 + 3*x^89 + 68*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 102*x^83 + 75*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 125*x^73 + 116*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 114*x^67 + 125*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 15*x^25 + 116*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 30*x^19 + 23*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 121*x^9 + 68*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 106*x^3 + 89*x + 64, x^93 + 74*x^91 + 36*x^90 + 75*x^89 + 84*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 12*x^82 + 67*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 85*x^73 + 28*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 4*x^66 + 101*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 119*x^25 + 100*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 124*x^18 + 111*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 113*x^9 + 44*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 116*x^2 + 33*x + 4, x^93 + 74*x^91 + 108*x^90 + 75*x^89 + 92*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 100*x^82 + 3*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 85*x^73 + 116*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 76*x^66 + 37*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 119*x^25 + 12*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 52*x^18 + 47*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 113*x^9 + 36*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 28*x^2 + 97*x + 44, x^93 + 74*x^91 + 64*x^90 + 35*x^89 + 64*x^88 + 68*x^87 + 64*x^86 + x^85 + 64*x^84 + 102*x^83 + 43*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 93*x^73 + 64*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 114*x^67 + 29*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 47*x^25 + 64*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 30*x^19 + 119*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 89*x^9 + 64*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 106*x^3 + 121*x, x^93 + 74*x^91 + 24*x^90 + 67*x^89 + 88*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 8*x^82 + 11*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 61*x^73 + 72*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 88*x^66 + 61*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 79*x^25 + 56*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 40*x^18 + 87*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 57*x^9 + 40*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 120*x^2 + 25*x + 120, x^93 + 74*x^91 + 52*x^90 + 11*x^89 + 100*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 124*x^82 + 67*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 21*x^73 + 76*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 84*x^66 + 101*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 55*x^25 + 52*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 44*x^18 + 111*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 49*x^9 + 28*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 4*x^2 + 33*x + 20, x^93 + 74*x^91 + 52*x^90 + 123*x^89 + 20*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 60*x^82 + 19*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 101*x^73 + 92*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 20*x^66 + 85*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 103*x^25 + 36*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 108*x^18 + 127*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 65*x^9 + 108*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 68*x^2 + 81*x + 68, x^93 + 74*x^91 + 124*x^90 + 27*x^89 + 124*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 84*x^82 + 115*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 69*x^73 + 84*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 28*x^66 + 117*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 7*x^25 + 44*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 100*x^18 + 95*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 33*x^9 + 4*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 44*x^2 + 113*x + 12, x^93 + 74*x^91 + 32*x^90 + 35*x^89 + 4*x^87 + 64*x^86 + 65*x^85 + 38*x^83 + 96*x^82 + 107*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 93*x^73 + 52*x^71 + 64*x^70 + 71*x^69 + 50*x^67 + 32*x^66 + 93*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 47*x^25 + 52*x^23 + 64*x^22 + 101*x^21 + 94*x^19 + 96*x^18 + 55*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 89*x^9 + 4*x^7 + 64*x^6 + 91*x^5 + 42*x^3 + 32*x^2 + 57*x, x^93 + 74*x^91 + 40*x^90 + 67*x^89 + 40*x^88 + 4*x^87 + 48*x^86 + x^85 + 112*x^84 + 38*x^83 + 120*x^82 + 75*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 61*x^73 + 56*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 40*x^66 + 125*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 79*x^25 + 72*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 88*x^18 + 23*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 57*x^9 + 88*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 8*x^2 + 89*x + 72, x^93 + 74*x^91 + 96*x^90 + 35*x^89 + 32*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 38*x^83 + 32*x^82 + 107*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 93*x^73 + 96*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 50*x^67 + 96*x^66 + 93*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 47*x^25 + 32*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 94*x^19 + 32*x^18 + 55*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 89*x^9 + 96*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 42*x^3 + 96*x^2 + 57*x + 32, x^93 + 74*x^91 + 16*x^90 + 67*x^89 + 48*x^88 + 4*x^87 + 96*x^86 + x^85 + 32*x^84 + 38*x^83 + 48*x^82 + 75*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 61*x^73 + 16*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 16*x^66 + 125*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 79*x^25 + 112*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 112*x^18 + 23*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 57*x^9 + 80*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 80*x^2 + 89*x + 112, x^93 + 74*x^91 + 20*x^90 + 27*x^89 + 116*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 92*x^82 + 115*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 69*x^73 + 124*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 116*x^66 + 117*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 7*x^25 + 4*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 12*x^18 + 95*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 33*x^9 + 12*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 36*x^2 + 113*x + 36, x^93 + 74*x^91 + 35*x^89 + 64*x^88 + 68*x^87 + 64*x^86 + x^85 + 64*x^84 + 102*x^83 + 64*x^82 + 43*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 93*x^73 + 64*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 114*x^67 + 64*x^66 + 29*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 47*x^25 + 64*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 30*x^19 + 64*x^18 + 119*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 89*x^9 + 64*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 106*x^3 + 64*x^2 + 121*x, x^93 + 74*x^91 + 72*x^90 + 3*x^89 + 40*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 24*x^82 + 75*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 125*x^73 + 56*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 8*x^66 + 125*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 15*x^25 + 72*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 120*x^18 + 23*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 121*x^9 + 88*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 104*x^2 + 89*x + 8, x^93 + 74*x^91 + 28*x^90 + 11*x^89 + 12*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 52*x^82 + 3*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 21*x^73 + 4*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 60*x^66 + 37*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 55*x^25 + 124*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 68*x^18 + 47*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 49*x^9 + 116*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 76*x^2 + 97*x + 92, x^93 + 74*x^91 + 99*x^89 + 32*x^88 + 4*x^87 + 65*x^85 + 64*x^84 + 38*x^83 + 43*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 29*x^73 + 96*x^72 + 52*x^71 + 71*x^69 + 64*x^68 + 50*x^67 + 29*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 111*x^25 + 32*x^24 + 52*x^23 + 101*x^21 + 64*x^20 + 94*x^19 + 119*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 25*x^9 + 96*x^8 + 4*x^7 + 91*x^5 + 64*x^4 + 42*x^3 + 121*x + 32, x^93 + 74*x^91 + 76*x^90 + 27*x^89 + 12*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 4*x^82 + 51*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 69*x^73 + 4*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 44*x^66 + 53*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 7*x^25 + 124*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 84*x^18 + 31*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 33*x^9 + 116*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 124*x^2 + 49*x + 28, x^93 + 74*x^91 + 40*x^90 + 3*x^89 + 104*x^88 + 4*x^87 + 48*x^86 + x^85 + 112*x^84 + 38*x^83 + 120*x^82 + 11*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 125*x^73 + 120*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 40*x^66 + 61*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 15*x^25 + 8*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 88*x^18 + 87*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 121*x^9 + 24*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 8*x^2 + 25*x + 8, x^93 + 74*x^91 + 20*x^90 + 27*x^89 + 116*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 28*x^82 + 51*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 69*x^73 + 124*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 52*x^66 + 53*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 7*x^25 + 4*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 76*x^18 + 31*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 33*x^9 + 12*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 100*x^2 + 49*x + 100, x^93 + 74*x^91 + 36*x^90 + 75*x^89 + 52*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 76*x^82 + 3*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 85*x^73 + 60*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 68*x^66 + 37*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 119*x^25 + 68*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 60*x^18 + 47*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 113*x^9 + 76*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 52*x^2 + 97*x + 36, x^93 + 74*x^91 + 4*x^90 + 27*x^89 + 100*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 44*x^82 + 115*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 69*x^73 + 76*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 100*x^66 + 117*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 7*x^25 + 52*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 28*x^18 + 95*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 33*x^9 + 28*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 84*x^2 + 113*x + 84, x^93 + 74*x^91 + 83*x^89 + 112*x^88 + 68*x^87 + 33*x^85 + 32*x^84 + 102*x^83 + 59*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 109*x^73 + 80*x^72 + 116*x^71 + 39*x^69 + 32*x^68 + 114*x^67 + 77*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 31*x^25 + 48*x^24 + 116*x^23 + 69*x^21 + 32*x^20 + 30*x^19 + 71*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 41*x^9 + 16*x^8 + 68*x^7 + 59*x^5 + 32*x^4 + 106*x^3 + 105*x + 48, x^93 + 74*x^91 + 40*x^90 + 3*x^89 + 72*x^88 + 4*x^87 + 48*x^86 + x^85 + 48*x^84 + 38*x^83 + 120*x^82 + 11*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 125*x^73 + 24*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 40*x^66 + 61*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 15*x^25 + 104*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 88*x^18 + 87*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 121*x^9 + 56*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 8*x^2 + 25*x + 104, x^93 + 74*x^91 + 84*x^90 + 59*x^89 + 116*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 92*x^82 + 19*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 37*x^73 + 124*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 116*x^66 + 85*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 39*x^25 + 4*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 12*x^18 + 127*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + x^9 + 12*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 36*x^2 + 81*x + 100, x^93 + 74*x^91 + 76*x^90 + 75*x^89 + 124*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 4*x^82 + 3*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 85*x^73 + 84*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 44*x^66 + 37*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 119*x^25 + 44*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 84*x^18 + 47*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 113*x^9 + 4*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 124*x^2 + 97*x + 76, x^93 + 74*x^91 + 92*x^90 + 27*x^89 + 92*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 116*x^82 + 115*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 69*x^73 + 116*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 124*x^66 + 117*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 7*x^25 + 12*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 4*x^18 + 95*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 33*x^9 + 36*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 12*x^2 + 113*x + 108, x^93 + 74*x^91 + 4*x^90 + 123*x^89 + 100*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 44*x^82 + 19*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 101*x^73 + 76*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 100*x^66 + 85*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 103*x^25 + 52*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 28*x^18 + 127*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 65*x^9 + 28*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 84*x^2 + 81*x + 84, x^93 + 74*x^91 + 92*x^90 + 107*x^89 + 44*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 52*x^82 + 99*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 53*x^73 + 100*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 60*x^66 + 69*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 23*x^25 + 28*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 68*x^18 + 15*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 81*x^9 + 84*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 76*x^2 + x + 60, x^93 + 74*x^91 + 92*x^90 + 43*x^89 + 76*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 116*x^82 + 99*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 117*x^73 + 68*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 124*x^66 + 69*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 87*x^25 + 60*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 4*x^18 + 15*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 17*x^9 + 52*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 12*x^2 + x + 28, x^93 + 74*x^91 + 99*x^89 + 4*x^87 + 65*x^85 + 38*x^83 + 43*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 29*x^73 + 52*x^71 + 71*x^69 + 50*x^67 + 29*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 111*x^25 + 52*x^23 + 101*x^21 + 94*x^19 + 119*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 25*x^9 + 4*x^7 + 91*x^5 + 42*x^3 + 121*x, x^93 + 74*x^91 + 8*x^90 + 83*x^89 + 56*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 24*x^82 + 59*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 109*x^73 + 104*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 8*x^66 + 77*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 31*x^25 + 24*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 120*x^18 + 71*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 41*x^9 + 72*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 104*x^2 + 105*x + 24, x^93 + 74*x^91 + 44*x^90 + 43*x^89 + 28*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 36*x^82 + 35*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 117*x^73 + 52*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 12*x^66 + 5*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 87*x^25 + 76*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 116*x^18 + 79*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 17*x^9 + 100*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 92*x^2 + 65*x + 108, x^93 + 74*x^91 + 116*x^90 + 123*x^89 + 52*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 60*x^82 + 83*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 101*x^73 + 60*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 20*x^66 + 21*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 103*x^25 + 68*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 108*x^18 + 63*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 65*x^9 + 76*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 68*x^2 + 17*x + 36, x^93 + 74*x^91 + 80*x^90 + 51*x^89 + 96*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 38*x^83 + 48*x^82 + 27*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 13*x^73 + 32*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 50*x^67 + 16*x^66 + 109*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 127*x^25 + 96*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 94*x^19 + 112*x^18 + 39*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 73*x^9 + 32*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 42*x^3 + 80*x^2 + 9*x + 32, x^93 + 74*x^91 + 35*x^89 + 4*x^87 + 65*x^85 + 38*x^83 + 107*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 93*x^73 + 52*x^71 + 71*x^69 + 50*x^67 + 93*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 47*x^25 + 52*x^23 + 101*x^21 + 94*x^19 + 55*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 89*x^9 + 4*x^7 + 91*x^5 + 42*x^3 + 57*x, x^93 + 74*x^91 + 8*x^90 + 83*x^89 + 56*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 88*x^82 + 123*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 109*x^73 + 104*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 72*x^66 + 13*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 31*x^25 + 24*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 56*x^18 + 7*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 41*x^9 + 72*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 40*x^2 + 41*x + 88, x^93 + 74*x^91 + 52*x^90 + 43*x^89 + 68*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 60*x^82 + 99*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 117*x^73 + 108*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 20*x^66 + 69*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 87*x^25 + 20*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 108*x^18 + 15*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 17*x^9 + 60*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 68*x^2 + x + 52, x^93 + 74*x^91 + 40*x^90 + 19*x^89 + 120*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 120*x^82 + 123*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 45*x^73 + 40*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 40*x^66 + 13*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 95*x^25 + 88*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 88*x^18 + 7*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 105*x^9 + 8*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 8*x^2 + 41*x + 88, x^93 + 74*x^91 + 12*x^90 + 75*x^89 + 28*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 4*x^82 + 67*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 85*x^73 + 52*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 44*x^66 + 101*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 119*x^25 + 76*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 84*x^18 + 111*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 113*x^9 + 100*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 124*x^2 + 33*x + 44, x^93 + 74*x^91 + 116*x^90 + 75*x^89 + 4*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 60*x^82 + 3*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 85*x^73 + 44*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 20*x^66 + 37*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 119*x^25 + 84*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 108*x^18 + 47*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 113*x^9 + 124*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 68*x^2 + 97*x + 52, x^93 + 74*x^91 + 24*x^90 + 19*x^89 + 72*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 72*x^82 + 123*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 45*x^73 + 24*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 24*x^66 + 13*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 95*x^25 + 104*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 104*x^18 + 7*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 105*x^9 + 56*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 56*x^2 + 41*x + 104, x^93 + 74*x^91 + 88*x^90 + 67*x^89 + 24*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 72*x^82 + 11*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 61*x^73 + 8*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 24*x^66 + 61*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 79*x^25 + 120*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 104*x^18 + 87*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 57*x^9 + 104*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 56*x^2 + 25*x + 56, x^93 + 74*x^91 + 8*x^90 + 115*x^89 + 88*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 24*x^82 + 27*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 77*x^73 + 72*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 8*x^66 + 109*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 63*x^25 + 56*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 120*x^18 + 39*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 9*x^9 + 40*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 104*x^2 + 9*x + 56, x^93 + 74*x^91 + 100*x^90 + 27*x^89 + 4*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 12*x^82 + 51*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 69*x^73 + 44*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 4*x^66 + 53*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 7*x^25 + 84*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 124*x^18 + 31*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 33*x^9 + 124*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 116*x^2 + 49*x + 52, x^93 + 74*x^91 + 104*x^90 + 3*x^89 + 104*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 120*x^82 + 75*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 125*x^73 + 120*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 40*x^66 + 125*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 15*x^25 + 8*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 88*x^18 + 23*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 121*x^9 + 24*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 8*x^2 + 89*x + 72, x^93 + 74*x^91 + 104*x^90 + 35*x^89 + 8*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 56*x^82 + 107*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 93*x^73 + 88*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 104*x^66 + 93*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 47*x^25 + 40*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 24*x^18 + 55*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 89*x^9 + 120*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 72*x^2 + 57*x + 40, x^93 + 74*x^91 + 40*x^90 + 83*x^89 + 120*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 56*x^82 + 123*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 109*x^73 + 40*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 104*x^66 + 13*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 31*x^25 + 88*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 24*x^18 + 7*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 41*x^9 + 8*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 72*x^2 + 41*x + 24, x^93 + 74*x^91 + 32*x^90 + 67*x^89 + 64*x^88 + 68*x^87 + 65*x^85 + 64*x^84 + 102*x^83 + 32*x^82 + 11*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 61*x^73 + 64*x^72 + 116*x^71 + 71*x^69 + 64*x^68 + 114*x^67 + 96*x^66 + 61*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 79*x^25 + 64*x^24 + 116*x^23 + 101*x^21 + 64*x^20 + 30*x^19 + 32*x^18 + 87*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 57*x^9 + 64*x^8 + 68*x^7 + 91*x^5 + 64*x^4 + 106*x^3 + 96*x^2 + 25*x, x^93 + 74*x^91 + 48*x^90 + 3*x^89 + 48*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 80*x^82 + 75*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 125*x^73 + 16*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 112*x^66 + 125*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 15*x^25 + 112*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 16*x^18 + 23*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 121*x^9 + 80*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 48*x^2 + 89*x + 48, x^93 + 74*x^91 + 36*x^90 + 59*x^89 + 100*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 76*x^82 + 19*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 37*x^73 + 76*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 68*x^66 + 85*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 39*x^25 + 52*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 60*x^18 + 127*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + x^9 + 28*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 52*x^2 + 81*x + 20, x^93 + 74*x^91 + 84*x^90 + 91*x^89 + 52*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 92*x^82 + 115*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 5*x^73 + 60*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 116*x^66 + 117*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 71*x^25 + 68*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 12*x^18 + 95*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 97*x^9 + 76*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 36*x^2 + 113*x + 36, x^93 + 74*x^91 + 52*x^90 + 43*x^89 + 100*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 124*x^82 + 35*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 117*x^73 + 76*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 84*x^66 + 5*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 87*x^25 + 52*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 44*x^18 + 79*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 17*x^9 + 28*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 4*x^2 + 65*x + 20, x^93 + 74*x^91 + 72*x^90 + 35*x^89 + 104*x^88 + 68*x^87 + 48*x^86 + x^85 + 48*x^84 + 102*x^83 + 24*x^82 + 43*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 93*x^73 + 120*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 8*x^66 + 29*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 47*x^25 + 8*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 120*x^18 + 119*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 89*x^9 + 24*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 104*x^2 + 121*x + 72, x^93 + 74*x^91 + 8*x^90 + 67*x^89 + 72*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 88*x^82 + 11*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 61*x^73 + 24*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 72*x^66 + 61*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 79*x^25 + 104*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 56*x^18 + 87*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 57*x^9 + 56*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 40*x^2 + 25*x + 40, x^93 + 74*x^91 + 100*x^90 + 11*x^89 + 52*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 76*x^82 + 3*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 21*x^73 + 60*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 68*x^66 + 37*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 55*x^25 + 68*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 60*x^18 + 47*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 49*x^9 + 76*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 52*x^2 + 97*x + 100, x^93 + 74*x^91 + 12*x^90 + 75*x^89 + 60*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 68*x^82 + 3*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 85*x^73 + 20*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 108*x^66 + 37*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 119*x^25 + 108*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 20*x^18 + 47*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 113*x^9 + 68*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 60*x^2 + 97*x + 12, x^93 + 74*x^91 + 52*x^90 + 91*x^89 + 52*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 60*x^82 + 51*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 5*x^73 + 60*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 20*x^66 + 53*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 71*x^25 + 68*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 108*x^18 + 31*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 97*x^9 + 76*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 68*x^2 + 49*x + 100, x^93 + 74*x^91 + 40*x^90 + 19*x^89 + 24*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 120*x^82 + 123*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 45*x^73 + 8*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 40*x^66 + 13*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 95*x^25 + 120*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 88*x^18 + 7*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 105*x^9 + 104*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 8*x^2 + 41*x + 120, x^93 + 74*x^91 + 68*x^90 + 27*x^89 + 4*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 108*x^82 + 115*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 69*x^73 + 44*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 36*x^66 + 117*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 7*x^25 + 84*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 92*x^18 + 95*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 33*x^9 + 124*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 20*x^2 + 113*x + 116, x^93 + 74*x^91 + 28*x^90 + 27*x^89 + 92*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 116*x^82 + 51*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 69*x^73 + 116*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 124*x^66 + 53*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 7*x^25 + 12*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 4*x^18 + 31*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 33*x^9 + 36*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 12*x^2 + 49*x + 44, x^93 + 74*x^91 + 48*x^90 + 35*x^89 + 80*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 16*x^82 + 107*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 93*x^73 + 112*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 48*x^66 + 93*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 47*x^25 + 16*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 80*x^18 + 55*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 89*x^9 + 48*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 112*x^2 + 57*x + 16, x^93 + 74*x^91 + 24*x^90 + 99*x^89 + 56*x^88 + 68*x^87 + 16*x^86 + x^85 + 16*x^84 + 102*x^83 + 8*x^82 + 107*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 29*x^73 + 104*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 88*x^66 + 93*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 111*x^25 + 24*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 40*x^18 + 55*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 25*x^9 + 72*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 120*x^2 + 57*x + 88, x^93 + 74*x^91 + 60*x^90 + 27*x^89 + 60*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 20*x^82 + 115*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 69*x^73 + 20*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 92*x^66 + 117*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 7*x^25 + 108*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 36*x^18 + 95*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 33*x^9 + 68*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 108*x^2 + 113*x + 76, x^93 + 74*x^91 + 52*x^90 + 107*x^89 + 68*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 60*x^82 + 35*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 53*x^73 + 108*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 20*x^66 + 5*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 23*x^25 + 20*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 108*x^18 + 79*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 81*x^9 + 60*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 68*x^2 + 65*x + 52, x^93 + 74*x^91 + 24*x^90 + 115*x^89 + 104*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 8*x^82 + 91*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 77*x^73 + 120*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 88*x^66 + 45*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 63*x^25 + 8*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 40*x^18 + 103*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 9*x^9 + 24*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 120*x^2 + 73*x + 72, x^93 + 74*x^91 + 88*x^90 + 3*x^89 + 56*x^88 + 4*x^87 + 80*x^86 + x^85 + 80*x^84 + 38*x^83 + 8*x^82 + 11*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 125*x^73 + 104*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 88*x^66 + 61*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 15*x^25 + 24*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 40*x^18 + 87*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 121*x^9 + 72*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 120*x^2 + 25*x + 24, x^93 + 74*x^91 + 72*x^90 + 99*x^89 + 8*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 88*x^82 + 43*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 29*x^73 + 88*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 72*x^66 + 29*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 111*x^25 + 40*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 56*x^18 + 119*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 25*x^9 + 120*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 40*x^2 + 121*x + 40, x^93 + 74*x^91 + 92*x^90 + 27*x^89 + 124*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 52*x^82 + 51*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 69*x^73 + 84*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 60*x^66 + 53*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 7*x^25 + 44*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 68*x^18 + 31*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 33*x^9 + 4*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 76*x^2 + 49*x + 76, x^93 + 74*x^91 + 64*x^90 + 19*x^89 + 16*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 38*x^83 + 59*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 45*x^73 + 48*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 50*x^67 + 77*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 95*x^25 + 80*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 94*x^19 + 71*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 105*x^9 + 112*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 42*x^3 + 105*x + 16, x^93 + 74*x^91 + 24*x^90 + 51*x^89 + 8*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 72*x^82 + 91*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 13*x^73 + 88*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 24*x^66 + 45*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 127*x^25 + 40*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 104*x^18 + 103*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 73*x^9 + 120*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 56*x^2 + 73*x + 40, x^93 + 74*x^91 + 76*x^90 + 27*x^89 + 108*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 68*x^82 + 115*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 69*x^73 + 36*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 108*x^66 + 117*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 7*x^25 + 92*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 20*x^18 + 95*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 33*x^9 + 20*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 60*x^2 + 113*x + 60, x^93 + 74*x^91 + 32*x^90 + 19*x^89 + 80*x^88 + 4*x^87 + 97*x^85 + 32*x^84 + 38*x^83 + 32*x^82 + 59*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 45*x^73 + 112*x^72 + 52*x^71 + 103*x^69 + 32*x^68 + 50*x^67 + 96*x^66 + 77*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 95*x^25 + 16*x^24 + 52*x^23 + 5*x^21 + 32*x^20 + 94*x^19 + 32*x^18 + 71*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 105*x^9 + 48*x^8 + 4*x^7 + 123*x^5 + 32*x^4 + 42*x^3 + 96*x^2 + 105*x + 80, x^93 + 74*x^91 + 8*x^90 + 83*x^89 + 24*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 88*x^82 + 123*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 109*x^73 + 8*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 72*x^66 + 13*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 31*x^25 + 120*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 56*x^18 + 7*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 41*x^9 + 104*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 40*x^2 + 41*x + 56, x^93 + 74*x^91 + 48*x^90 + 115*x^89 + 64*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 80*x^82 + 91*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 77*x^73 + 64*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 112*x^66 + 45*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 63*x^25 + 64*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 16*x^18 + 103*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 9*x^9 + 64*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 48*x^2 + 73*x, x^93 + 74*x^91 + 20*x^90 + 27*x^89 + 52*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 28*x^82 + 51*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 69*x^73 + 60*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 52*x^66 + 53*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 7*x^25 + 68*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 76*x^18 + 31*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 33*x^9 + 76*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 100*x^2 + 49*x + 36, x^93 + 74*x^91 + 56*x^90 + 67*x^89 + 88*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 104*x^82 + 11*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 61*x^73 + 72*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 120*x^66 + 61*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 79*x^25 + 56*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 8*x^18 + 87*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 57*x^9 + 40*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 24*x^2 + 25*x + 120, x^93 + 74*x^91 + 52*x^90 + 107*x^89 + 36*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 60*x^82 + 35*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 53*x^73 + 12*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 20*x^66 + 5*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 23*x^25 + 116*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 108*x^18 + 79*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 81*x^9 + 92*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 68*x^2 + 65*x + 20, x^93 + 74*x^91 + 28*x^90 + 123*x^89 + 60*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 116*x^82 + 83*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 101*x^73 + 20*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 124*x^66 + 21*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 103*x^25 + 108*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 4*x^18 + 63*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 65*x^9 + 68*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 12*x^2 + 17*x + 12, x^93 + 74*x^91 + 32*x^90 + 67*x^89 + 32*x^88 + 4*x^87 + 64*x^86 + x^85 + 64*x^84 + 38*x^83 + 96*x^82 + 75*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 61*x^73 + 96*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 50*x^67 + 32*x^66 + 125*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 79*x^25 + 32*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 94*x^19 + 96*x^18 + 23*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 57*x^9 + 96*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 42*x^3 + 32*x^2 + 89*x + 32, x^93 + 74*x^91 + 52*x^90 + 107*x^89 + 100*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 124*x^82 + 99*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 53*x^73 + 76*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 84*x^66 + 69*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 23*x^25 + 52*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 44*x^18 + 15*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 81*x^9 + 28*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 4*x^2 + x + 20, x^93 + 74*x^91 + 8*x^90 + 3*x^89 + 40*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 88*x^82 + 75*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 125*x^73 + 56*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 72*x^66 + 125*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 15*x^25 + 72*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 56*x^18 + 23*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 121*x^9 + 88*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 40*x^2 + 89*x + 8, x^93 + 74*x^91 + 108*x^90 + 107*x^89 + 60*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 36*x^82 + 35*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 53*x^73 + 20*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 12*x^66 + 5*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 23*x^25 + 108*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 116*x^18 + 79*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 81*x^9 + 68*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 92*x^2 + 65*x + 76, x^93 + 74*x^91 + 124*x^90 + 59*x^89 + 92*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 20*x^82 + 19*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 37*x^73 + 116*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 92*x^66 + 85*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 39*x^25 + 12*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 36*x^18 + 127*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + x^9 + 36*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 108*x^2 + 81*x + 44, x^93 + 74*x^91 + 76*x^90 + 59*x^89 + 12*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 4*x^82 + 19*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 37*x^73 + 4*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 44*x^66 + 85*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 39*x^25 + 124*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 84*x^18 + 127*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + x^9 + 116*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 124*x^2 + 81*x + 28, x^93 + 74*x^91 + 16*x^90 + 51*x^89 + 96*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 38*x^83 + 112*x^82 + 27*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 13*x^73 + 32*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 50*x^67 + 80*x^66 + 109*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 127*x^25 + 96*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 94*x^19 + 48*x^18 + 39*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 73*x^9 + 32*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 42*x^3 + 16*x^2 + 9*x + 32, x^93 + 74*x^91 + 24*x^90 + 115*x^89 + 72*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 72*x^82 + 27*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 77*x^73 + 24*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 24*x^66 + 109*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 63*x^25 + 104*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 104*x^18 + 39*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 9*x^9 + 56*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 56*x^2 + 9*x + 104, x^93 + 74*x^91 + 60*x^90 + 91*x^89 + 124*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 84*x^82 + 115*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 5*x^73 + 84*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 28*x^66 + 117*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 71*x^25 + 44*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 100*x^18 + 95*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 97*x^9 + 4*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 44*x^2 + 113*x + 76, x^93 + 74*x^91 + 24*x^90 + 35*x^89 + 56*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 72*x^82 + 107*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 93*x^73 + 104*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 24*x^66 + 93*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 47*x^25 + 24*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 104*x^18 + 55*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 89*x^9 + 72*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 56*x^2 + 57*x + 24, x^93 + 74*x^91 + 84*x^90 + 123*x^89 + 116*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 28*x^82 + 19*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 101*x^73 + 124*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 52*x^66 + 85*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 103*x^25 + 4*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 76*x^18 + 127*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 65*x^9 + 12*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 100*x^2 + 81*x + 36, x^93 + 74*x^91 + 124*x^90 + 59*x^89 + 92*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 84*x^82 + 83*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 37*x^73 + 116*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 28*x^66 + 21*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 39*x^25 + 12*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 100*x^18 + 63*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + x^9 + 36*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 44*x^2 + 17*x + 108, x^93 + 74*x^91 + 44*x^90 + 107*x^89 + 60*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 100*x^82 + 35*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 53*x^73 + 20*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 76*x^66 + 5*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 23*x^25 + 108*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 52*x^18 + 79*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 81*x^9 + 68*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 28*x^2 + 65*x + 76, x^93 + 74*x^91 + 40*x^90 + 99*x^89 + 8*x^88 + 68*x^87 + 112*x^86 + x^85 + 112*x^84 + 102*x^83 + 56*x^82 + 107*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 29*x^73 + 88*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 104*x^66 + 93*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 111*x^25 + 40*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 24*x^18 + 55*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 25*x^9 + 120*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 72*x^2 + 57*x + 104, x^93 + 74*x^91 + 8*x^90 + 19*x^89 + 56*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 88*x^82 + 59*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 45*x^73 + 104*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 72*x^66 + 77*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 95*x^25 + 24*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 56*x^18 + 71*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 105*x^9 + 72*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 40*x^2 + 105*x + 88, x^93 + 74*x^91 + 40*x^90 + 3*x^89 + 40*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 56*x^82 + 75*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 125*x^73 + 56*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 104*x^66 + 125*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 15*x^25 + 72*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 24*x^18 + 23*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 121*x^9 + 88*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 72*x^2 + 89*x + 8, x^93 + 74*x^91 + 20*x^90 + 11*x^89 + 4*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 28*x^82 + 67*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 21*x^73 + 44*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 52*x^66 + 101*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 55*x^25 + 84*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 76*x^18 + 111*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 49*x^9 + 124*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 100*x^2 + 33*x + 52, x^93 + 74*x^91 + 32*x^90 + 3*x^89 + 96*x^88 + 68*x^87 + 65*x^85 + 102*x^83 + 32*x^82 + 75*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 125*x^73 + 32*x^72 + 116*x^71 + 71*x^69 + 114*x^67 + 96*x^66 + 125*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 15*x^25 + 96*x^24 + 116*x^23 + 101*x^21 + 30*x^19 + 32*x^18 + 23*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 121*x^9 + 32*x^8 + 68*x^7 + 91*x^5 + 106*x^3 + 96*x^2 + 89*x + 32, x^93 + 74*x^91 + 84*x^90 + 11*x^89 + 4*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 28*x^82 + 3*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 21*x^73 + 44*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 52*x^66 + 37*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 55*x^25 + 84*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 76*x^18 + 47*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 49*x^9 + 124*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 100*x^2 + 97*x + 116, x^93 + 74*x^91 + 44*x^90 + 27*x^89 + 108*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 100*x^82 + 115*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 69*x^73 + 36*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 76*x^66 + 117*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 7*x^25 + 92*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 52*x^18 + 95*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 33*x^9 + 20*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 28*x^2 + 113*x + 60, x^93 + 74*x^91 + 120*x^90 + 115*x^89 + 40*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 40*x^82 + 91*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 77*x^73 + 56*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 56*x^66 + 45*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 63*x^25 + 72*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 72*x^18 + 103*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 9*x^9 + 88*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 88*x^2 + 73*x + 8, x^93 + 74*x^91 + 44*x^90 + 59*x^89 + 76*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 36*x^82 + 19*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 37*x^73 + 68*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 12*x^66 + 85*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 39*x^25 + 60*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 116*x^18 + 127*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + x^9 + 52*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 92*x^2 + 81*x + 92, x^93 + 74*x^91 + 48*x^90 + 51*x^89 + 4*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 80*x^82 + 27*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 13*x^73 + 52*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 112*x^66 + 109*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 127*x^25 + 52*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 16*x^18 + 39*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 73*x^9 + 4*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 48*x^2 + 9*x + 64, x^93 + 74*x^91 + 12*x^90 + 27*x^89 + 44*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 4*x^82 + 115*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 69*x^73 + 100*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 44*x^66 + 117*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 7*x^25 + 28*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 84*x^18 + 95*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 33*x^9 + 84*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 124*x^2 + 113*x + 124, x^93 + 74*x^91 + 16*x^90 + 99*x^89 + 16*x^88 + 68*x^87 + 32*x^86 + x^85 + 32*x^84 + 102*x^83 + 112*x^82 + 107*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 29*x^73 + 48*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 80*x^66 + 93*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 111*x^25 + 80*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 48*x^18 + 55*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 25*x^9 + 112*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 16*x^2 + 57*x + 16, x^93 + 74*x^91 + 112*x^90 + 51*x^89 + 64*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 16*x^82 + 27*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 13*x^73 + 64*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 48*x^66 + 109*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 127*x^25 + 64*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 80*x^18 + 39*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 73*x^9 + 64*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 112*x^2 + 9*x, x^93 + 74*x^91 + 96*x^90 + 115*x^89 + 16*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 102*x^83 + 32*x^82 + 27*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 77*x^73 + 48*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 114*x^67 + 96*x^66 + 109*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 63*x^25 + 80*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 30*x^19 + 32*x^18 + 39*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 9*x^9 + 112*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 106*x^3 + 96*x^2 + 9*x + 80, x^93 + 74*x^91 + 72*x^90 + 51*x^89 + 56*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 88*x^82 + 91*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 13*x^73 + 104*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 72*x^66 + 45*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 127*x^25 + 24*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 56*x^18 + 103*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 73*x^9 + 72*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 40*x^2 + 73*x + 24, x^93 + 74*x^91 + 52*x^90 + 91*x^89 + 116*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 60*x^82 + 51*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 5*x^73 + 124*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 20*x^66 + 53*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 71*x^25 + 4*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 108*x^18 + 31*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 97*x^9 + 12*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 68*x^2 + 49*x + 36, x^93 + 74*x^91 + 48*x^90 + 19*x^89 + 32*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 38*x^83 + 80*x^82 + 59*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 45*x^73 + 96*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 50*x^67 + 112*x^66 + 77*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 95*x^25 + 32*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 94*x^19 + 16*x^18 + 71*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 105*x^9 + 96*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 42*x^3 + 48*x^2 + 105*x + 96, x^93 + 74*x^91 + 92*x^90 + 91*x^89 + 124*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 116*x^82 + 51*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 5*x^73 + 84*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 124*x^66 + 53*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 71*x^25 + 44*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 4*x^18 + 31*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 97*x^9 + 4*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 12*x^2 + 49*x + 12, x^93 + 74*x^91 + 67*x^89 + 4*x^87 + x^85 + 38*x^83 + 75*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 61*x^73 + 52*x^71 + 7*x^69 + 50*x^67 + 125*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 79*x^25 + 52*x^23 + 37*x^21 + 94*x^19 + 23*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 57*x^9 + 4*x^7 + 27*x^5 + 42*x^3 + 89*x, x^93 + 74*x^91 + 56*x^90 + 67*x^89 + 88*x^88 + 4*x^87 + 16*x^86 + x^85 + 16*x^84 + 38*x^83 + 40*x^82 + 75*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 61*x^73 + 72*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 56*x^66 + 125*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 79*x^25 + 56*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 72*x^18 + 23*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 57*x^9 + 40*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 88*x^2 + 89*x + 56, x^93 + 74*x^91 + 84*x^90 + 75*x^89 + 68*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 92*x^82 + 3*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 85*x^73 + 108*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 116*x^66 + 37*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 119*x^25 + 20*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 12*x^18 + 47*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 113*x^9 + 60*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 36*x^2 + 97*x + 116, x^93 + 74*x^91 + 108*x^90 + 123*x^89 + 76*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 100*x^82 + 83*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 101*x^73 + 68*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 76*x^66 + 21*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 103*x^25 + 60*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 52*x^18 + 63*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 65*x^9 + 52*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 28*x^2 + 17*x + 92, x^93 + 74*x^91 + 12*x^90 + 107*x^89 + 92*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 4*x^82 + 35*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 53*x^73 + 116*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 44*x^66 + 5*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 23*x^25 + 12*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 84*x^18 + 79*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 81*x^9 + 36*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 124*x^2 + 65*x + 108, x^93 + 74*x^91 + 80*x^90 + 83*x^89 + 4*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 48*x^82 + 123*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 109*x^73 + 52*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 16*x^66 + 13*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 31*x^25 + 52*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 112*x^18 + 7*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 41*x^9 + 4*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 80*x^2 + 41*x + 64, x^93 + 74*x^91 + 16*x^90 + 19*x^89 + 64*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 102*x^83 + 48*x^82 + 123*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 45*x^73 + 64*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 114*x^67 + 16*x^66 + 13*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 95*x^25 + 64*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 30*x^19 + 112*x^18 + 7*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 105*x^9 + 64*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 106*x^3 + 80*x^2 + 41*x + 64, x^93 + 74*x^91 + 68*x^90 + 123*x^89 + 4*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 108*x^82 + 19*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 101*x^73 + 44*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 36*x^66 + 85*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 103*x^25 + 84*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 92*x^18 + 127*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 65*x^9 + 124*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 20*x^2 + 81*x + 116, x^93 + 74*x^91 + 12*x^90 + 11*x^89 + 92*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 4*x^82 + 3*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 21*x^73 + 116*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 44*x^66 + 37*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 55*x^25 + 12*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 84*x^18 + 47*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 49*x^9 + 36*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 124*x^2 + 97*x + 108, x^93 + 74*x^91 + 8*x^90 + 3*x^89 + 104*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 88*x^82 + 75*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 125*x^73 + 120*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 72*x^66 + 125*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 15*x^25 + 8*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 56*x^18 + 23*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 121*x^9 + 24*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 40*x^2 + 89*x + 72, x^93 + 74*x^91 + 16*x^90 + 19*x^89 + 32*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 48*x^82 + 123*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 45*x^73 + 96*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 16*x^66 + 13*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 95*x^25 + 32*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 112*x^18 + 7*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 105*x^9 + 96*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 80*x^2 + 41*x + 32, x^93 + 74*x^91 + 48*x^90 + 99*x^89 + 48*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 16*x^82 + 43*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 29*x^73 + 16*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 48*x^66 + 29*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 111*x^25 + 112*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 80*x^18 + 119*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 25*x^9 + 80*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 112*x^2 + 121*x + 112, x^93 + 74*x^91 + 28*x^90 + 59*x^89 + 28*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 52*x^82 + 83*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 37*x^73 + 52*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 60*x^66 + 21*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 39*x^25 + 76*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 68*x^18 + 63*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + x^9 + 100*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 76*x^2 + 17*x + 44, x^93 + 74*x^91 + 28*x^90 + 27*x^89 + 124*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 52*x^82 + 115*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 69*x^73 + 84*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 60*x^66 + 117*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 7*x^25 + 44*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 68*x^18 + 95*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 33*x^9 + 4*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 76*x^2 + 113*x + 12, x^93 + 74*x^91 + 92*x^90 + 43*x^89 + 44*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 116*x^82 + 99*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 117*x^73 + 100*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 124*x^66 + 69*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 87*x^25 + 28*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 4*x^18 + 15*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 17*x^9 + 84*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 12*x^2 + x + 124, x^93 + 74*x^91 + 104*x^90 + 67*x^89 + 8*x^88 + 4*x^87 + 48*x^86 + x^85 + 48*x^84 + 38*x^83 + 56*x^82 + 75*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 61*x^73 + 88*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 104*x^66 + 125*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 79*x^25 + 40*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 24*x^18 + 23*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 57*x^9 + 120*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 72*x^2 + 89*x + 40, x^93 + 74*x^91 + 48*x^90 + 83*x^89 + 96*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 38*x^83 + 80*x^82 + 123*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 109*x^73 + 32*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 50*x^67 + 112*x^66 + 13*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 31*x^25 + 96*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 94*x^19 + 16*x^18 + 7*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 41*x^9 + 32*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 42*x^3 + 48*x^2 + 41*x + 32, x^93 + 74*x^91 + 24*x^90 + 115*x^89 + 40*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 8*x^82 + 91*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 77*x^73 + 56*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 88*x^66 + 45*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 63*x^25 + 72*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 40*x^18 + 103*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 9*x^9 + 88*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 120*x^2 + 73*x + 8, x^93 + 74*x^91 + 36*x^90 + 107*x^89 + 116*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 76*x^82 + 99*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 53*x^73 + 124*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 68*x^66 + 69*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 23*x^25 + 4*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 60*x^18 + 15*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 81*x^9 + 12*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 52*x^2 + x + 100, x^93 + 74*x^91 + 40*x^90 + 83*x^89 + 56*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 120*x^82 + 59*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 109*x^73 + 104*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 40*x^66 + 77*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 31*x^25 + 24*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 88*x^18 + 71*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 41*x^9 + 72*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 8*x^2 + 105*x + 24, x^93 + 74*x^91 + 40*x^90 + 83*x^89 + 88*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 56*x^82 + 123*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 109*x^73 + 72*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 104*x^66 + 13*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 31*x^25 + 56*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 24*x^18 + 7*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 41*x^9 + 40*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 72*x^2 + 41*x + 120, x^93 + 74*x^91 + 68*x^90 + 11*x^89 + 116*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 44*x^82 + 67*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 21*x^73 + 124*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 100*x^66 + 101*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 55*x^25 + 4*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 28*x^18 + 111*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 49*x^9 + 12*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 84*x^2 + 33*x + 100, x^93 + 74*x^91 + 76*x^90 + 11*x^89 + 60*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 4*x^82 + 67*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 21*x^73 + 20*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 44*x^66 + 101*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 55*x^25 + 108*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 84*x^18 + 111*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 49*x^9 + 68*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 124*x^2 + 33*x + 12, x^93 + 74*x^91 + 28*x^90 + 59*x^89 + 92*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 116*x^82 + 19*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 37*x^73 + 116*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 124*x^66 + 85*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 39*x^25 + 12*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 4*x^18 + 127*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + x^9 + 36*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 12*x^2 + 81*x + 44, x^93 + 74*x^91 + 48*x^90 + 99*x^89 + 16*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 16*x^82 + 43*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 29*x^73 + 48*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 48*x^66 + 29*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 111*x^25 + 80*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 80*x^18 + 119*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 25*x^9 + 112*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 112*x^2 + 121*x + 80, x^93 + 74*x^91 + 36*x^90 + 91*x^89 + 100*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 12*x^82 + 51*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 5*x^73 + 76*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 4*x^66 + 53*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 71*x^25 + 52*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 124*x^18 + 31*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 97*x^9 + 28*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 116*x^2 + 49*x + 84, x^93 + 74*x^91 + 16*x^90 + 115*x^89 + 32*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 48*x^82 + 27*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 77*x^73 + 96*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 16*x^66 + 109*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 63*x^25 + 32*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 112*x^18 + 39*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 9*x^9 + 96*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 80*x^2 + 9*x + 32, x^93 + 74*x^91 + 52*x^90 + 27*x^89 + 116*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 124*x^82 + 51*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 69*x^73 + 124*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 84*x^66 + 53*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 7*x^25 + 4*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 44*x^18 + 31*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 33*x^9 + 12*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 4*x^2 + 49*x + 100, x^93 + 74*x^91 + 4*x^90 + 91*x^89 + 36*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 108*x^82 + 115*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 5*x^73 + 12*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 36*x^66 + 117*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 71*x^25 + 116*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 92*x^18 + 95*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 97*x^9 + 92*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 20*x^2 + 113*x + 84, x^93 + 74*x^91 + 64*x^90 + 115*x^89 + 80*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 38*x^83 + 91*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 77*x^73 + 112*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 50*x^67 + 45*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 63*x^25 + 16*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 94*x^19 + 103*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 9*x^9 + 48*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 42*x^3 + 73*x + 80, x^93 + 74*x^91 + 24*x^90 + 19*x^89 + 40*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 8*x^82 + 59*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 45*x^73 + 56*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 88*x^66 + 77*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 95*x^25 + 72*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 40*x^18 + 71*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 105*x^9 + 88*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 120*x^2 + 105*x + 8, x^93 + 74*x^91 + 100*x^90 + 107*x^89 + 84*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 12*x^82 + 99*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 53*x^73 + 28*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 4*x^66 + 69*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 23*x^25 + 100*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 124*x^18 + 15*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 81*x^9 + 44*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 116*x^2 + x + 68, x^93 + 74*x^91 + 44*x^90 + 91*x^89 + 108*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 36*x^82 + 115*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 5*x^73 + 36*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 12*x^66 + 117*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 71*x^25 + 92*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 116*x^18 + 95*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 97*x^9 + 20*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 92*x^2 + 113*x + 124, x^93 + 74*x^91 + 36*x^90 + 27*x^89 + 68*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 12*x^82 + 115*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 69*x^73 + 108*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 4*x^66 + 117*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 7*x^25 + 20*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 124*x^18 + 95*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 33*x^9 + 60*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 116*x^2 + 113*x + 52, x^93 + 74*x^91 + 96*x^90 + 115*x^89 + 80*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 102*x^83 + 32*x^82 + 27*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 77*x^73 + 112*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 114*x^67 + 96*x^66 + 109*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 63*x^25 + 16*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 30*x^19 + 32*x^18 + 39*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 9*x^9 + 48*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 106*x^3 + 96*x^2 + 9*x + 16, x^93 + 74*x^91 + 124*x^90 + 11*x^89 + 44*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 20*x^82 + 67*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 21*x^73 + 100*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 92*x^66 + 101*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 55*x^25 + 28*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 36*x^18 + 111*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 49*x^9 + 84*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 108*x^2 + 33*x + 60, x^93 + 74*x^91 + 120*x^90 + 3*x^89 + 56*x^88 + 4*x^87 + 16*x^86 + x^85 + 80*x^84 + 38*x^83 + 104*x^82 + 11*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 125*x^73 + 104*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 120*x^66 + 61*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 15*x^25 + 24*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 8*x^18 + 87*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 121*x^9 + 72*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 24*x^2 + 25*x + 24, x^93 + 74*x^91 + 44*x^90 + 11*x^89 + 92*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 100*x^82 + 3*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 21*x^73 + 116*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 76*x^66 + 37*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 55*x^25 + 12*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 52*x^18 + 47*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 49*x^9 + 36*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 28*x^2 + 97*x + 108, x^93 + 74*x^91 + 20*x^90 + 59*x^89 + 52*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 28*x^82 + 19*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 37*x^73 + 60*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 52*x^66 + 85*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 39*x^25 + 68*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 76*x^18 + 127*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + x^9 + 76*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 100*x^2 + 81*x + 36, x^93 + 74*x^91 + 8*x^90 + 83*x^89 + 120*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 24*x^82 + 59*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 109*x^73 + 40*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 8*x^66 + 77*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 31*x^25 + 88*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 120*x^18 + 71*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 41*x^9 + 8*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 104*x^2 + 105*x + 88, x^93 + 74*x^91 + 32*x^90 + 99*x^89 + 68*x^87 + x^85 + 64*x^84 + 102*x^83 + 32*x^82 + 107*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 29*x^73 + 116*x^71 + 7*x^69 + 64*x^68 + 114*x^67 + 96*x^66 + 93*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 111*x^25 + 116*x^23 + 37*x^21 + 64*x^20 + 30*x^19 + 32*x^18 + 55*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 25*x^9 + 68*x^7 + 27*x^5 + 64*x^4 + 106*x^3 + 96*x^2 + 57*x + 64, x^93 + 74*x^91 + 104*x^90 + 51*x^89 + 120*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 120*x^82 + 27*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 13*x^73 + 40*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 40*x^66 + 109*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 127*x^25 + 88*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 88*x^18 + 39*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 73*x^9 + 8*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 8*x^2 + 9*x + 24, x^93 + 74*x^91 + 60*x^90 + 27*x^89 + 60*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 84*x^82 + 51*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 69*x^73 + 20*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 28*x^66 + 53*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 7*x^25 + 108*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 100*x^18 + 31*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 33*x^9 + 68*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 44*x^2 + 49*x + 12, x^93 + 74*x^91 + 100*x^90 + 75*x^89 + 84*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 12*x^82 + 3*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 85*x^73 + 28*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 4*x^66 + 37*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 119*x^25 + 100*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 124*x^18 + 47*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 113*x^9 + 44*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 116*x^2 + 97*x + 68, x^93 + 74*x^91 + 64*x^90 + 99*x^89 + 96*x^88 + 68*x^87 + 64*x^86 + x^85 + 102*x^83 + 107*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 29*x^73 + 32*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 114*x^67 + 93*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 111*x^25 + 96*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 30*x^19 + 55*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 25*x^9 + 32*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 106*x^3 + 57*x + 32, x^93 + 74*x^91 + 32*x^90 + 115*x^89 + 16*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 102*x^83 + 96*x^82 + 27*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 77*x^73 + 48*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 114*x^67 + 32*x^66 + 109*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 63*x^25 + 80*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 30*x^19 + 96*x^18 + 39*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 9*x^9 + 112*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 106*x^3 + 32*x^2 + 9*x + 80, x^93 + 74*x^91 + 36*x^90 + 27*x^89 + 68*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 76*x^82 + 51*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 69*x^73 + 108*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 68*x^66 + 53*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 7*x^25 + 20*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 60*x^18 + 31*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 33*x^9 + 60*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 52*x^2 + 49*x + 116, x^93 + 74*x^91 + 44*x^90 + 59*x^89 + 12*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 36*x^82 + 19*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 37*x^73 + 4*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 12*x^66 + 85*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 39*x^25 + 124*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 116*x^18 + 127*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + x^9 + 116*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 92*x^2 + 81*x + 28, x^93 + 74*x^91 + 28*x^90 + 91*x^89 + 28*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 116*x^82 + 115*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 5*x^73 + 52*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 124*x^66 + 117*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 71*x^25 + 76*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 4*x^18 + 95*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 97*x^9 + 100*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 12*x^2 + 113*x + 108, x^93 + 74*x^91 + 48*x^90 + 99*x^89 + 112*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 16*x^82 + 43*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 29*x^73 + 80*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 48*x^66 + 29*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 111*x^25 + 48*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 80*x^18 + 119*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 25*x^9 + 16*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 112*x^2 + 121*x + 48, x^93 + 74*x^91 + 12*x^90 + 123*x^89 + 76*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 68*x^82 + 83*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 101*x^73 + 68*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 108*x^66 + 21*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 103*x^25 + 60*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 20*x^18 + 63*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 65*x^9 + 52*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 60*x^2 + 17*x + 92, x^93 + 74*x^91 + 88*x^90 + 115*x^89 + 8*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 8*x^82 + 27*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 77*x^73 + 88*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 88*x^66 + 109*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 63*x^25 + 40*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 40*x^18 + 39*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 9*x^9 + 120*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 120*x^2 + 9*x + 40, x^93 + 74*x^91 + 120*x^90 + 67*x^89 + 56*x^88 + 4*x^87 + 16*x^86 + x^85 + 80*x^84 + 38*x^83 + 104*x^82 + 75*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 61*x^73 + 104*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 120*x^66 + 125*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 79*x^25 + 24*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 8*x^18 + 23*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 57*x^9 + 72*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 24*x^2 + 89*x + 24, x^93 + 74*x^91 + 4*x^90 + 75*x^89 + 20*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 108*x^82 + 3*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 85*x^73 + 92*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 36*x^66 + 37*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 119*x^25 + 36*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 92*x^18 + 47*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 113*x^9 + 108*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 20*x^2 + 97*x + 4, x^93 + 74*x^91 + 88*x^90 + 3*x^89 + 56*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 72*x^82 + 75*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 125*x^73 + 104*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 24*x^66 + 125*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 15*x^25 + 24*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 104*x^18 + 23*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 121*x^9 + 72*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 56*x^2 + 89*x + 88, x^93 + 74*x^91 + 112*x^90 + 35*x^89 + 112*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 80*x^82 + 107*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 93*x^73 + 80*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 112*x^66 + 93*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 47*x^25 + 48*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 16*x^18 + 55*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 89*x^9 + 16*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 48*x^2 + 57*x + 48, x^93 + 74*x^91 + 88*x^90 + 115*x^89 + 8*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 72*x^82 + 91*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 77*x^73 + 88*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 24*x^66 + 45*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 63*x^25 + 40*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 104*x^18 + 103*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 9*x^9 + 120*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 56*x^2 + 73*x + 104, x^93 + 74*x^91 + 4*x^90 + 107*x^89 + 116*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 44*x^82 + 35*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 53*x^73 + 124*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 100*x^66 + 5*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 23*x^25 + 4*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 28*x^18 + 79*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 81*x^9 + 12*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 84*x^2 + 65*x + 36, x^93 + 74*x^91 + 52*x^90 + 107*x^89 + 68*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 124*x^82 + 99*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 53*x^73 + 108*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 84*x^66 + 69*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 23*x^25 + 20*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 44*x^18 + 15*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 81*x^9 + 60*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 4*x^2 + x + 116, x^93 + 74*x^91 + 24*x^90 + 19*x^89 + 104*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 8*x^82 + 59*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 45*x^73 + 120*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 88*x^66 + 77*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 95*x^25 + 8*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 40*x^18 + 71*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 105*x^9 + 24*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 120*x^2 + 105*x + 72, x^93 + 74*x^91 + 76*x^90 + 123*x^89 + 76*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 68*x^82 + 19*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 101*x^73 + 68*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 108*x^66 + 85*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 103*x^25 + 60*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 20*x^18 + 127*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 65*x^9 + 52*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 60*x^2 + 81*x + 28, x^93 + 74*x^91 + 16*x^90 + 19*x^89 + 68*x^87 + 96*x^86 + 33*x^85 + 102*x^83 + 48*x^82 + 123*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 45*x^73 + 116*x^71 + 96*x^70 + 39*x^69 + 114*x^67 + 16*x^66 + 13*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 95*x^25 + 116*x^23 + 96*x^22 + 69*x^21 + 30*x^19 + 112*x^18 + 7*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 105*x^9 + 68*x^7 + 96*x^6 + 59*x^5 + 106*x^3 + 80*x^2 + 41*x, x^93 + 74*x^91 + 28*x^90 + 75*x^89 + 12*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 52*x^82 + 67*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 85*x^73 + 4*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 60*x^66 + 101*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 119*x^25 + 124*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 68*x^18 + 111*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 113*x^9 + 116*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 76*x^2 + 33*x + 92, x^93 + 74*x^91 + 60*x^90 + 11*x^89 + 108*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 20*x^82 + 3*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 21*x^73 + 36*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 92*x^66 + 37*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 55*x^25 + 92*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 36*x^18 + 47*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 49*x^9 + 20*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 108*x^2 + 97*x + 60, x^93 + 74*x^91 + 88*x^90 + 67*x^89 + 88*x^88 + 4*x^87 + 80*x^86 + x^85 + 16*x^84 + 38*x^83 + 8*x^82 + 75*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 61*x^73 + 72*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 88*x^66 + 125*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 79*x^25 + 56*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 40*x^18 + 23*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 57*x^9 + 40*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 120*x^2 + 89*x + 56, x^93 + 74*x^91 + 36*x^90 + 43*x^89 + 84*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 12*x^82 + 99*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 117*x^73 + 28*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 4*x^66 + 69*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 87*x^25 + 100*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 124*x^18 + 15*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 17*x^9 + 44*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 116*x^2 + x + 4, x^93 + 74*x^91 + 80*x^90 + 19*x^89 + 96*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 38*x^83 + 48*x^82 + 59*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 45*x^73 + 32*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 50*x^67 + 16*x^66 + 77*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 95*x^25 + 96*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 94*x^19 + 112*x^18 + 71*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 105*x^9 + 32*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 42*x^3 + 80*x^2 + 105*x + 32, x^93 + 74*x^91 + 20*x^90 + 107*x^89 + 4*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 28*x^82 + 99*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 53*x^73 + 44*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 52*x^66 + 69*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 23*x^25 + 84*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 76*x^18 + 15*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 81*x^9 + 124*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 100*x^2 + x + 52, x^93 + 74*x^91 + 4*x^90 + 123*x^89 + 100*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 108*x^82 + 83*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 101*x^73 + 76*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 36*x^66 + 21*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 103*x^25 + 52*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 92*x^18 + 63*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 65*x^9 + 28*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 20*x^2 + 17*x + 20, x^93 + 74*x^91 + 120*x^90 + 67*x^89 + 24*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 40*x^82 + 11*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 61*x^73 + 8*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 56*x^66 + 61*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 79*x^25 + 120*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 72*x^18 + 87*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 57*x^9 + 104*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 88*x^2 + 25*x + 56, x^93 + 74*x^91 + 68*x^90 + 91*x^89 + 4*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 44*x^82 + 115*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 5*x^73 + 44*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 100*x^66 + 117*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 71*x^25 + 84*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 28*x^18 + 95*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 97*x^9 + 124*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 84*x^2 + 113*x + 52, x^93 + 74*x^91 + 24*x^90 + 67*x^89 + 120*x^88 + 4*x^87 + 80*x^86 + x^85 + 80*x^84 + 38*x^83 + 72*x^82 + 75*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 61*x^73 + 40*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 24*x^66 + 125*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 79*x^25 + 88*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 104*x^18 + 23*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 57*x^9 + 8*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 56*x^2 + 89*x + 88, x^93 + 74*x^91 + 64*x^90 + 3*x^89 + 96*x^88 + 4*x^87 + x^85 + 64*x^84 + 38*x^83 + 64*x^82 + 11*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 125*x^73 + 32*x^72 + 52*x^71 + 7*x^69 + 64*x^68 + 50*x^67 + 64*x^66 + 61*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 15*x^25 + 96*x^24 + 52*x^23 + 37*x^21 + 64*x^20 + 94*x^19 + 64*x^18 + 87*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 121*x^9 + 32*x^8 + 4*x^7 + 27*x^5 + 64*x^4 + 42*x^3 + 64*x^2 + 25*x + 96, x^93 + 74*x^91 + 32*x^90 + 99*x^89 + 96*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 38*x^83 + 96*x^82 + 43*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 29*x^73 + 32*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 50*x^67 + 32*x^66 + 29*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 111*x^25 + 96*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 94*x^19 + 96*x^18 + 119*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 25*x^9 + 32*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 42*x^3 + 32*x^2 + 121*x + 96, x^93 + 74*x^91 + 56*x^90 + 115*x^89 + 40*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 104*x^82 + 91*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 77*x^73 + 56*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 120*x^66 + 45*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 63*x^25 + 72*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 8*x^18 + 103*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 9*x^9 + 88*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 24*x^2 + 73*x + 8, x^93 + 74*x^91 + 32*x^90 + 83*x^89 + 112*x^88 + 4*x^87 + 97*x^85 + 96*x^84 + 38*x^83 + 32*x^82 + 123*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 109*x^73 + 80*x^72 + 52*x^71 + 103*x^69 + 96*x^68 + 50*x^67 + 96*x^66 + 13*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 31*x^25 + 48*x^24 + 52*x^23 + 5*x^21 + 96*x^20 + 94*x^19 + 32*x^18 + 7*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 41*x^9 + 16*x^8 + 4*x^7 + 123*x^5 + 96*x^4 + 42*x^3 + 96*x^2 + 41*x + 112, x^93 + 74*x^91 + 96*x^90 + 115*x^89 + 80*x^88 + 4*x^87 + 33*x^85 + 32*x^84 + 38*x^83 + 96*x^82 + 91*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 77*x^73 + 112*x^72 + 52*x^71 + 39*x^69 + 32*x^68 + 50*x^67 + 32*x^66 + 45*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 63*x^25 + 16*x^24 + 52*x^23 + 69*x^21 + 32*x^20 + 94*x^19 + 96*x^18 + 103*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 9*x^9 + 48*x^8 + 4*x^7 + 59*x^5 + 32*x^4 + 42*x^3 + 32*x^2 + 73*x + 80, x^93 + 74*x^91 + 48*x^90 + 51*x^89 + 96*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 16*x^82 + 91*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 13*x^73 + 32*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 48*x^66 + 45*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 127*x^25 + 96*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 80*x^18 + 103*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 73*x^9 + 32*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 112*x^2 + 73*x + 96, x^93 + 74*x^91 + 28*x^90 + 43*x^89 + 108*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 116*x^82 + 35*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 117*x^73 + 36*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 124*x^66 + 5*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 87*x^25 + 92*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 4*x^18 + 79*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 17*x^9 + 20*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 12*x^2 + 65*x + 124, x^93 + 74*x^91 + 108*x^90 + 75*x^89 + 124*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 100*x^82 + 3*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 85*x^73 + 84*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 76*x^66 + 37*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 119*x^25 + 44*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 52*x^18 + 47*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 113*x^9 + 4*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 28*x^2 + 97*x + 76, x^93 + 74*x^91 + 120*x^90 + 51*x^89 + 8*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 104*x^82 + 91*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 13*x^73 + 88*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 120*x^66 + 45*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 127*x^25 + 40*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 8*x^18 + 103*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 73*x^9 + 120*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 24*x^2 + 73*x + 40, x^93 + 74*x^91 + 24*x^90 + 51*x^89 + 40*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 8*x^82 + 27*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 13*x^73 + 56*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 88*x^66 + 109*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 127*x^25 + 72*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 40*x^18 + 39*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 73*x^9 + 88*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 120*x^2 + 9*x + 8, x^93 + 74*x^91 + 4*x^90 + 43*x^89 + 116*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 44*x^82 + 99*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 117*x^73 + 124*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 100*x^66 + 69*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 87*x^25 + 4*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 28*x^18 + 15*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 17*x^9 + 12*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 84*x^2 + x + 36, x^93 + 74*x^91 + 64*x^90 + 19*x^89 + 80*x^88 + 68*x^87 + 33*x^85 + 96*x^84 + 102*x^83 + 64*x^82 + 123*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 45*x^73 + 112*x^72 + 116*x^71 + 39*x^69 + 96*x^68 + 114*x^67 + 64*x^66 + 13*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 95*x^25 + 16*x^24 + 116*x^23 + 69*x^21 + 96*x^20 + 30*x^19 + 64*x^18 + 7*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 105*x^9 + 48*x^8 + 68*x^7 + 59*x^5 + 96*x^4 + 106*x^3 + 64*x^2 + 41*x + 16, x^93 + 74*x^91 + 48*x^90 + 35*x^89 + 48*x^88 + 68*x^87 + 96*x^86 + x^85 + 96*x^84 + 102*x^83 + 80*x^82 + 43*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 93*x^73 + 16*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 112*x^66 + 29*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 47*x^25 + 112*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 16*x^18 + 119*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 89*x^9 + 80*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 48*x^2 + 121*x + 48, x^93 + 74*x^91 + 120*x^90 + 99*x^89 + 120*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 104*x^82 + 43*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 29*x^73 + 40*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 120*x^66 + 29*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 111*x^25 + 88*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 8*x^18 + 119*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 25*x^9 + 8*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 24*x^2 + 121*x + 88, x^93 + 74*x^91 + 68*x^90 + 11*x^89 + 52*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 108*x^82 + 3*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 21*x^73 + 60*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 36*x^66 + 37*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 55*x^25 + 68*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 92*x^18 + 47*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 49*x^9 + 76*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 20*x^2 + 97*x + 100, x^93 + 74*x^91 + 112*x^90 + 83*x^89 + 68*x^87 + 32*x^86 + 33*x^85 + 102*x^83 + 80*x^82 + 59*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 109*x^73 + 116*x^71 + 32*x^70 + 39*x^69 + 114*x^67 + 112*x^66 + 77*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 31*x^25 + 116*x^23 + 32*x^22 + 69*x^21 + 30*x^19 + 16*x^18 + 71*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 41*x^9 + 68*x^7 + 32*x^6 + 59*x^5 + 106*x^3 + 48*x^2 + 105*x, x^93 + 74*x^91 + 124*x^90 + 91*x^89 + 92*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 20*x^82 + 115*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 5*x^73 + 116*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 92*x^66 + 117*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 71*x^25 + 12*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 36*x^18 + 95*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 97*x^9 + 36*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 108*x^2 + 113*x + 44, x^93 + 74*x^91 + 108*x^90 + 75*x^89 + 60*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 36*x^82 + 67*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 85*x^73 + 20*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 12*x^66 + 101*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 119*x^25 + 108*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 116*x^18 + 111*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 113*x^9 + 68*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 92*x^2 + 33*x + 76, x^93 + 74*x^91 + 92*x^90 + 43*x^89 + 44*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 52*x^82 + 35*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 117*x^73 + 100*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 60*x^66 + 5*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 87*x^25 + 28*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 68*x^18 + 79*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 17*x^9 + 84*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 76*x^2 + 65*x + 60, x^93 + 74*x^91 + 20*x^90 + 91*x^89 + 84*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 28*x^82 + 115*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 5*x^73 + 28*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 52*x^66 + 117*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 71*x^25 + 100*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 76*x^18 + 95*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 97*x^9 + 44*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 100*x^2 + 113*x + 68, x^93 + 74*x^91 + 104*x^90 + 3*x^89 + 104*x^88 + 4*x^87 + 48*x^86 + x^85 + 112*x^84 + 38*x^83 + 56*x^82 + 11*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 125*x^73 + 120*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 104*x^66 + 61*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 15*x^25 + 8*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 24*x^18 + 87*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 121*x^9 + 24*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 72*x^2 + 25*x + 8, x^93 + 74*x^91 + 108*x^90 + 43*x^89 + 60*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 36*x^82 + 99*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 117*x^73 + 20*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 12*x^66 + 69*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 87*x^25 + 108*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 116*x^18 + 15*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 17*x^9 + 68*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 92*x^2 + x + 76, x^93 + 74*x^91 + 88*x^90 + 115*x^89 + 104*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 72*x^82 + 91*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 77*x^73 + 120*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 24*x^66 + 45*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 63*x^25 + 8*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 104*x^18 + 103*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 9*x^9 + 24*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 56*x^2 + 73*x + 72, x^93 + 74*x^91 + 108*x^90 + 123*x^89 + 108*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 100*x^82 + 83*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 101*x^73 + 36*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 76*x^66 + 21*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 103*x^25 + 92*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 52*x^18 + 63*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 65*x^9 + 20*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 28*x^2 + 17*x + 124, x^93 + 74*x^91 + 112*x^90 + 115*x^89 + 68*x^87 + 32*x^86 + 97*x^85 + 102*x^83 + 80*x^82 + 27*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 77*x^73 + 116*x^71 + 32*x^70 + 103*x^69 + 114*x^67 + 112*x^66 + 109*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 63*x^25 + 116*x^23 + 32*x^22 + 5*x^21 + 30*x^19 + 16*x^18 + 39*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 9*x^9 + 68*x^7 + 32*x^6 + 123*x^5 + 106*x^3 + 48*x^2 + 9*x, x^93 + 74*x^91 + 92*x^90 + 11*x^89 + 12*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 116*x^82 + 3*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 21*x^73 + 4*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 124*x^66 + 37*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 55*x^25 + 124*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 4*x^18 + 47*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 49*x^9 + 116*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 12*x^2 + 97*x + 92, x^93 + 74*x^91 + 28*x^90 + 91*x^89 + 92*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 116*x^82 + 115*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 5*x^73 + 116*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 124*x^66 + 117*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 71*x^25 + 12*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 4*x^18 + 95*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 97*x^9 + 36*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 12*x^2 + 113*x + 44, x^93 + 74*x^91 + 4*x^90 + 75*x^89 + 20*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 44*x^82 + 67*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 85*x^73 + 92*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 100*x^66 + 101*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 119*x^25 + 36*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 28*x^18 + 111*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 113*x^9 + 108*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 84*x^2 + 33*x + 68, x^93 + 74*x^91 + 56*x^90 + 99*x^89 + 56*x^88 + 68*x^87 + 80*x^86 + x^85 + 16*x^84 + 102*x^83 + 104*x^82 + 107*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 29*x^73 + 104*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 120*x^66 + 93*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 111*x^25 + 24*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 8*x^18 + 55*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 25*x^9 + 72*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 24*x^2 + 57*x + 88, x^93 + 74*x^91 + 12*x^90 + 75*x^89 + 28*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 68*x^82 + 3*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 85*x^73 + 52*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 108*x^66 + 37*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 119*x^25 + 76*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 20*x^18 + 47*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 113*x^9 + 100*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 60*x^2 + 97*x + 108, x^93 + 74*x^91 + 104*x^90 + 83*x^89 + 120*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 56*x^82 + 59*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 109*x^73 + 40*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 104*x^66 + 77*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 31*x^25 + 88*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 24*x^18 + 71*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 41*x^9 + 8*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 72*x^2 + 105*x + 88, x^93 + 74*x^91 + 80*x^90 + 35*x^89 + 48*x^88 + 68*x^87 + 32*x^86 + x^85 + 96*x^84 + 102*x^83 + 48*x^82 + 43*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 93*x^73 + 16*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 16*x^66 + 29*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 47*x^25 + 112*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 112*x^18 + 119*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 89*x^9 + 80*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 80*x^2 + 121*x + 48, x^93 + 74*x^91 + 100*x^90 + 59*x^89 + 4*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 12*x^82 + 19*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 37*x^73 + 44*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 4*x^66 + 85*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 39*x^25 + 84*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 124*x^18 + 127*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + x^9 + 124*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 116*x^2 + 81*x + 52, x^93 + 74*x^91 + 12*x^90 + 123*x^89 + 44*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 68*x^82 + 83*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 101*x^73 + 100*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 108*x^66 + 21*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 103*x^25 + 28*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 20*x^18 + 63*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 65*x^9 + 84*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 60*x^2 + 17*x + 60, x^93 + 74*x^91 + 20*x^90 + 75*x^89 + 100*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 28*x^82 + 3*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 85*x^73 + 76*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 52*x^66 + 37*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 119*x^25 + 52*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 76*x^18 + 47*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 113*x^9 + 28*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 100*x^2 + 97*x + 20, x^93 + 74*x^91 + 80*x^90 + 51*x^89 + 32*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 112*x^82 + 91*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 13*x^73 + 96*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 80*x^66 + 45*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 127*x^25 + 32*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 48*x^18 + 103*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 73*x^9 + 96*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 16*x^2 + 73*x + 32, x^93 + 74*x^91 + 84*x^90 + 43*x^89 + 36*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 92*x^82 + 35*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 117*x^73 + 12*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 116*x^66 + 5*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 87*x^25 + 116*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 12*x^18 + 79*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 17*x^9 + 92*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 36*x^2 + 65*x + 84, x^93 + 74*x^91 + 36*x^90 + 59*x^89 + 68*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 76*x^82 + 19*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 37*x^73 + 108*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 68*x^66 + 85*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 39*x^25 + 20*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 60*x^18 + 127*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + x^9 + 60*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 52*x^2 + 81*x + 116, x^93 + 74*x^91 + 68*x^90 + 91*x^89 + 4*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 108*x^82 + 51*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 5*x^73 + 44*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 36*x^66 + 53*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 71*x^25 + 84*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 92*x^18 + 31*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 97*x^9 + 124*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 20*x^2 + 49*x + 116, x^93 + 74*x^91 + 96*x^90 + 115*x^89 + 16*x^88 + 4*x^87 + 33*x^85 + 32*x^84 + 38*x^83 + 96*x^82 + 91*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 77*x^73 + 48*x^72 + 52*x^71 + 39*x^69 + 32*x^68 + 50*x^67 + 32*x^66 + 45*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 63*x^25 + 80*x^24 + 52*x^23 + 69*x^21 + 32*x^20 + 94*x^19 + 96*x^18 + 103*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 9*x^9 + 112*x^8 + 4*x^7 + 59*x^5 + 32*x^4 + 42*x^3 + 32*x^2 + 73*x + 16, x^93 + 74*x^91 + 60*x^90 + 123*x^89 + 92*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 84*x^82 + 83*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 101*x^73 + 116*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 28*x^66 + 21*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 103*x^25 + 12*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 100*x^18 + 63*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 65*x^9 + 36*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 44*x^2 + 17*x + 44, x^93 + 74*x^91 + 60*x^90 + 27*x^89 + 28*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 20*x^82 + 115*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 69*x^73 + 52*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 92*x^66 + 117*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 7*x^25 + 76*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 36*x^18 + 95*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 33*x^9 + 100*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 108*x^2 + 113*x + 44, x^93 + 74*x^91 + 80*x^90 + 3*x^89 + 48*x^88 + 4*x^87 + 96*x^86 + x^85 + 32*x^84 + 38*x^83 + 112*x^82 + 11*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 125*x^73 + 16*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 80*x^66 + 61*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 15*x^25 + 112*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 48*x^18 + 87*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 121*x^9 + 80*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 16*x^2 + 25*x + 112, x^93 + 74*x^91 + 88*x^90 + 19*x^89 + 40*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 8*x^82 + 123*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 45*x^73 + 56*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 88*x^66 + 13*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 95*x^25 + 72*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 40*x^18 + 7*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 105*x^9 + 88*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 120*x^2 + 41*x + 72, x^93 + 74*x^91 + 40*x^90 + 83*x^89 + 88*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 120*x^82 + 59*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 109*x^73 + 72*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 40*x^66 + 77*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 31*x^25 + 56*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 88*x^18 + 71*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 41*x^9 + 40*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 8*x^2 + 105*x + 56, x^93 + 74*x^91 + 72*x^90 + 51*x^89 + 120*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 24*x^82 + 27*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 13*x^73 + 40*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 8*x^66 + 109*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 127*x^25 + 88*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 120*x^18 + 39*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 73*x^9 + 8*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 104*x^2 + 9*x + 24, x^93 + 74*x^91 + 40*x^90 + 3*x^89 + 104*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 56*x^82 + 75*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 125*x^73 + 120*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 104*x^66 + 125*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 15*x^25 + 8*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 24*x^18 + 23*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 121*x^9 + 24*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 72*x^2 + 89*x + 72, x^93 + 74*x^91 + 52*x^90 + 123*x^89 + 84*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 60*x^82 + 19*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 101*x^73 + 28*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 20*x^66 + 85*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 103*x^25 + 100*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 108*x^18 + 127*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 65*x^9 + 44*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 68*x^2 + 81*x + 4, x^93 + 74*x^91 + 104*x^90 + 19*x^89 + 88*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 56*x^82 + 123*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 45*x^73 + 72*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 104*x^66 + 13*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 95*x^25 + 56*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 24*x^18 + 7*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 105*x^9 + 40*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 72*x^2 + 41*x + 56, x^93 + 74*x^91 + 100*x^90 + 11*x^89 + 20*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 12*x^82 + 67*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 21*x^73 + 92*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 4*x^66 + 101*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 55*x^25 + 36*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 124*x^18 + 111*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 49*x^9 + 108*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 116*x^2 + 33*x + 4, x^93 + 74*x^91 + 68*x^90 + 107*x^89 + 84*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 108*x^82 + 35*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 53*x^73 + 28*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 36*x^66 + 5*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 23*x^25 + 100*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 92*x^18 + 79*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 81*x^9 + 44*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 20*x^2 + 65*x + 4, x^93 + 74*x^91 + 92*x^90 + 59*x^89 + 60*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 116*x^82 + 83*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 37*x^73 + 20*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 124*x^66 + 21*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 39*x^25 + 108*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 4*x^18 + 63*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + x^9 + 68*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 12*x^2 + 17*x + 76, x^93 + 74*x^91 + 112*x^90 + 99*x^89 + 48*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 80*x^82 + 43*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 29*x^73 + 16*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 112*x^66 + 29*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 111*x^25 + 112*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 16*x^18 + 119*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 25*x^9 + 80*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 48*x^2 + 121*x + 112, x^93 + 74*x^91 + 56*x^90 + 19*x^89 + 8*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 104*x^82 + 59*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 45*x^73 + 88*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 120*x^66 + 77*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 95*x^25 + 40*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 8*x^18 + 71*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 105*x^9 + 120*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 24*x^2 + 105*x + 104, x^93 + 74*x^91 + 100*x^90 + 59*x^89 + 100*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 12*x^82 + 19*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 37*x^73 + 76*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 4*x^66 + 85*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 39*x^25 + 52*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 124*x^18 + 127*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + x^9 + 28*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 116*x^2 + 81*x + 20, x^93 + 74*x^91 + 52*x^90 + 11*x^89 + 4*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 124*x^82 + 67*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 21*x^73 + 44*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 84*x^66 + 101*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 55*x^25 + 84*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 44*x^18 + 111*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 49*x^9 + 124*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 4*x^2 + 33*x + 52, x^93 + 74*x^91 + 40*x^90 + 3*x^89 + 72*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 56*x^82 + 75*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 125*x^73 + 24*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 104*x^66 + 125*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 15*x^25 + 104*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 24*x^18 + 23*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 121*x^9 + 56*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 72*x^2 + 89*x + 40, x^93 + 74*x^91 + 28*x^90 + 107*x^89 + 108*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 116*x^82 + 99*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 53*x^73 + 36*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 124*x^66 + 69*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 23*x^25 + 92*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 4*x^18 + 15*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 81*x^9 + 20*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 12*x^2 + x + 124, x^93 + 74*x^91 + 44*x^90 + 27*x^89 + 108*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 36*x^82 + 51*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 69*x^73 + 36*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 12*x^66 + 53*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 7*x^25 + 92*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 116*x^18 + 31*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 33*x^9 + 20*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 92*x^2 + 49*x + 124, x^93 + 74*x^91 + 80*x^90 + 115*x^89 + 96*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 38*x^83 + 48*x^82 + 91*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 77*x^73 + 32*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 50*x^67 + 16*x^66 + 45*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 63*x^25 + 96*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 94*x^19 + 112*x^18 + 103*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 9*x^9 + 32*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 42*x^3 + 80*x^2 + 73*x + 32, x^93 + 74*x^91 + 92*x^90 + 123*x^89 + 124*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 52*x^82 + 83*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 101*x^73 + 84*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 60*x^66 + 21*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 103*x^25 + 44*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 68*x^18 + 63*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 65*x^9 + 4*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 76*x^2 + 17*x + 76, x^93 + 74*x^91 + 100*x^90 + 59*x^89 + 36*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 76*x^82 + 83*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 37*x^73 + 12*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 68*x^66 + 21*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 39*x^25 + 116*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 60*x^18 + 63*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + x^9 + 92*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 52*x^2 + 17*x + 20, x^93 + 74*x^91 + 24*x^90 + 3*x^89 + 24*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 8*x^82 + 75*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 125*x^73 + 8*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 88*x^66 + 125*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 15*x^25 + 120*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 40*x^18 + 23*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 121*x^9 + 104*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 120*x^2 + 89*x + 56, x^93 + 74*x^91 + 116*x^90 + 75*x^89 + 36*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 60*x^82 + 3*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 85*x^73 + 12*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 20*x^66 + 37*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 119*x^25 + 116*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 108*x^18 + 47*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 113*x^9 + 92*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 68*x^2 + 97*x + 84, x^93 + 74*x^91 + 4*x^90 + 75*x^89 + 84*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 108*x^82 + 3*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 85*x^73 + 28*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 36*x^66 + 37*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 119*x^25 + 100*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 92*x^18 + 47*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 113*x^9 + 44*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 20*x^2 + 97*x + 68, x^93 + 74*x^91 + 112*x^90 + 83*x^89 + 96*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 38*x^83 + 16*x^82 + 123*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 109*x^73 + 32*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 50*x^67 + 48*x^66 + 13*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 31*x^25 + 96*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 94*x^19 + 80*x^18 + 7*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 41*x^9 + 32*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 42*x^3 + 112*x^2 + 41*x + 32, x^93 + 74*x^91 + 84*x^90 + 27*x^89 + 20*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 92*x^82 + 51*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 69*x^73 + 92*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 116*x^66 + 53*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 7*x^25 + 36*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 12*x^18 + 31*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 33*x^9 + 108*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 36*x^2 + 49*x + 4, x^93 + 74*x^91 + 104*x^90 + 67*x^89 + 8*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 120*x^82 + 11*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 61*x^73 + 88*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 40*x^66 + 61*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 79*x^25 + 40*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 88*x^18 + 87*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 57*x^9 + 120*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 8*x^2 + 25*x + 104, x^93 + 74*x^91 + 36*x^90 + 123*x^89 + 36*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 12*x^82 + 19*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 101*x^73 + 12*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 4*x^66 + 85*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 103*x^25 + 116*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 124*x^18 + 127*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 65*x^9 + 92*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 116*x^2 + 81*x + 20, x^93 + 74*x^91 + 28*x^90 + 91*x^89 + 60*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 52*x^82 + 51*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 5*x^73 + 20*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 60*x^66 + 53*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 71*x^25 + 108*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 68*x^18 + 31*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 97*x^9 + 68*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 76*x^2 + 49*x + 76, x^93 + 74*x^91 + 84*x^90 + 107*x^89 + 36*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 92*x^82 + 99*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 53*x^73 + 12*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 116*x^66 + 69*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 23*x^25 + 116*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 12*x^18 + 15*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 81*x^9 + 92*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 36*x^2 + x + 84, x^93 + 74*x^91 + 100*x^90 + 43*x^89 + 20*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 76*x^82 + 99*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 117*x^73 + 92*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 68*x^66 + 69*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 87*x^25 + 36*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 60*x^18 + 15*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 17*x^9 + 108*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 52*x^2 + x + 68, x^93 + 74*x^91 + 32*x^90 + 115*x^89 + 48*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 102*x^83 + 96*x^82 + 27*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 77*x^73 + 16*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 114*x^67 + 32*x^66 + 109*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 63*x^25 + 112*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 30*x^19 + 96*x^18 + 39*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 9*x^9 + 80*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 106*x^3 + 32*x^2 + 9*x + 112, x^93 + 74*x^91 + 52*x^90 + 27*x^89 + 52*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 60*x^82 + 115*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 69*x^73 + 60*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 20*x^66 + 117*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 7*x^25 + 68*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 108*x^18 + 95*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 33*x^9 + 76*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 68*x^2 + 113*x + 100, x^93 + 74*x^91 + 116*x^90 + 43*x^89 + 100*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 60*x^82 + 35*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 117*x^73 + 76*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 20*x^66 + 5*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 87*x^25 + 52*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 108*x^18 + 79*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 17*x^9 + 28*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 68*x^2 + 65*x + 20, x^93 + 74*x^91 + 96*x^90 + 19*x^89 + 16*x^88 + 4*x^87 + 97*x^85 + 32*x^84 + 38*x^83 + 96*x^82 + 59*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 45*x^73 + 48*x^72 + 52*x^71 + 103*x^69 + 32*x^68 + 50*x^67 + 32*x^66 + 77*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 95*x^25 + 80*x^24 + 52*x^23 + 5*x^21 + 32*x^20 + 94*x^19 + 96*x^18 + 71*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 105*x^9 + 112*x^8 + 4*x^7 + 123*x^5 + 32*x^4 + 42*x^3 + 32*x^2 + 105*x + 16, x^93 + 74*x^91 + 120*x^90 + 115*x^89 + 72*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 40*x^82 + 91*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 77*x^73 + 24*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 56*x^66 + 45*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 63*x^25 + 104*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 72*x^18 + 103*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 9*x^9 + 56*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 88*x^2 + 73*x + 40, x^93 + 74*x^91 + 8*x^90 + 67*x^89 + 8*x^88 + 4*x^87 + 112*x^86 + x^85 + 48*x^84 + 38*x^83 + 24*x^82 + 75*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 61*x^73 + 88*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 8*x^66 + 125*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 79*x^25 + 40*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 120*x^18 + 23*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 57*x^9 + 120*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 104*x^2 + 89*x + 40, x^93 + 74*x^91 + 16*x^90 + 115*x^89 + 96*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 48*x^82 + 27*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 77*x^73 + 32*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 16*x^66 + 109*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 63*x^25 + 96*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 112*x^18 + 39*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 9*x^9 + 32*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 80*x^2 + 9*x + 96, x^93 + 74*x^91 + 16*x^90 + 3*x^89 + 112*x^88 + 4*x^87 + 96*x^86 + x^85 + 32*x^84 + 38*x^83 + 48*x^82 + 11*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 125*x^73 + 80*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 16*x^66 + 61*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 15*x^25 + 48*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 112*x^18 + 87*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 121*x^9 + 16*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 80*x^2 + 25*x + 48, x^93 + 74*x^91 + 12*x^90 + 75*x^89 + 124*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 4*x^82 + 67*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 85*x^73 + 84*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 44*x^66 + 101*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 119*x^25 + 44*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 84*x^18 + 111*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 113*x^9 + 4*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 124*x^2 + 33*x + 12, x^93 + 74*x^91 + 60*x^90 + 107*x^89 + 108*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 20*x^82 + 35*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 53*x^73 + 36*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 92*x^66 + 5*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 23*x^25 + 92*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 36*x^18 + 79*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 81*x^9 + 20*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 108*x^2 + 65*x + 60, x^93 + 74*x^91 + 104*x^90 + 19*x^89 + 56*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 56*x^82 + 123*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 45*x^73 + 104*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 104*x^66 + 13*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 95*x^25 + 24*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 24*x^18 + 7*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 105*x^9 + 72*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 72*x^2 + 41*x + 24, x^93 + 74*x^91 + 32*x^90 + 19*x^89 + 112*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 102*x^83 + 96*x^82 + 123*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 45*x^73 + 80*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 114*x^67 + 32*x^66 + 13*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 95*x^25 + 48*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 30*x^19 + 96*x^18 + 7*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 105*x^9 + 16*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 106*x^3 + 32*x^2 + 41*x + 48, x^93 + 74*x^91 + 72*x^90 + 99*x^89 + 72*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 88*x^82 + 43*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 29*x^73 + 24*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 72*x^66 + 29*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 111*x^25 + 104*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 56*x^18 + 119*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 25*x^9 + 56*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 40*x^2 + 121*x + 104, x^93 + 74*x^91 + 108*x^90 + 91*x^89 + 76*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 36*x^82 + 51*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 5*x^73 + 68*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 12*x^66 + 53*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 71*x^25 + 60*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 116*x^18 + 31*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 97*x^9 + 52*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 92*x^2 + 49*x + 28, x^93 + 74*x^91 + 12*x^90 + 43*x^89 + 124*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 4*x^82 + 99*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 117*x^73 + 84*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 44*x^66 + 69*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 87*x^25 + 44*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 84*x^18 + 15*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 17*x^9 + 4*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 124*x^2 + x + 12, x^93 + 74*x^91 + 4*x^90 + 91*x^89 + 68*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 108*x^82 + 115*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 5*x^73 + 108*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 36*x^66 + 117*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 71*x^25 + 20*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 92*x^18 + 95*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 97*x^9 + 60*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 20*x^2 + 113*x + 116, x^93 + 74*x^91 + 64*x^90 + 19*x^89 + 112*x^88 + 68*x^87 + 33*x^85 + 32*x^84 + 102*x^83 + 64*x^82 + 123*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 45*x^73 + 80*x^72 + 116*x^71 + 39*x^69 + 32*x^68 + 114*x^67 + 64*x^66 + 13*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 95*x^25 + 48*x^24 + 116*x^23 + 69*x^21 + 32*x^20 + 30*x^19 + 64*x^18 + 7*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 105*x^9 + 16*x^8 + 68*x^7 + 59*x^5 + 32*x^4 + 106*x^3 + 64*x^2 + 41*x + 48, x^93 + 74*x^91 + 88*x^90 + 99*x^89 + 120*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 8*x^82 + 43*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 29*x^73 + 40*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 88*x^66 + 29*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 111*x^25 + 88*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 40*x^18 + 119*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 25*x^9 + 8*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 120*x^2 + 121*x + 88, x^93 + 74*x^91 + 68*x^90 + 43*x^89 + 116*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 108*x^82 + 99*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 117*x^73 + 124*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 36*x^66 + 69*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 87*x^25 + 4*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 92*x^18 + 15*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 17*x^9 + 12*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 20*x^2 + x + 36, x^93 + 74*x^91 + 112*x^90 + 3*x^89 + 112*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 16*x^82 + 75*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 125*x^73 + 80*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 48*x^66 + 125*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 15*x^25 + 48*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 80*x^18 + 23*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 121*x^9 + 16*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 112*x^2 + 89*x + 112, x^93 + 74*x^91 + 12*x^90 + 59*x^89 + 76*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 68*x^82 + 19*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 37*x^73 + 68*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 108*x^66 + 85*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 39*x^25 + 60*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 20*x^18 + 127*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + x^9 + 52*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 60*x^2 + 81*x + 92, x^93 + 74*x^91 + 48*x^90 + 67*x^89 + 80*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 80*x^82 + 11*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 61*x^73 + 112*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 112*x^66 + 61*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 79*x^25 + 16*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 16*x^18 + 87*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 57*x^9 + 48*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 48*x^2 + 25*x + 80, x^93 + 74*x^91 + 104*x^90 + 115*x^89 + 24*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 120*x^82 + 91*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 77*x^73 + 8*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 40*x^66 + 45*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 63*x^25 + 120*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 88*x^18 + 103*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 9*x^9 + 104*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 8*x^2 + 73*x + 56, x^93 + 74*x^91 + 124*x^90 + 75*x^89 + 76*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 84*x^82 + 67*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 85*x^73 + 68*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 28*x^66 + 101*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 119*x^25 + 60*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 100*x^18 + 111*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 113*x^9 + 52*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 44*x^2 + 33*x + 28, x^93 + 74*x^91 + 108*x^90 + 75*x^89 + 28*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 36*x^82 + 67*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 85*x^73 + 52*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 12*x^66 + 101*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 119*x^25 + 76*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 116*x^18 + 111*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 113*x^9 + 100*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 92*x^2 + 33*x + 44, x^93 + 74*x^91 + 4*x^90 + 27*x^89 + 100*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 108*x^82 + 51*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 69*x^73 + 76*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 36*x^66 + 53*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 7*x^25 + 52*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 92*x^18 + 31*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 33*x^9 + 28*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 20*x^2 + 49*x + 20, x^93 + 74*x^91 + 68*x^90 + 59*x^89 + 100*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 108*x^82 + 83*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 37*x^73 + 76*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 36*x^66 + 21*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 39*x^25 + 52*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 92*x^18 + 63*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + x^9 + 28*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 20*x^2 + 17*x + 84, x^93 + 74*x^91 + 24*x^90 + 3*x^89 + 56*x^88 + 4*x^87 + 80*x^86 + x^85 + 80*x^84 + 38*x^83 + 72*x^82 + 11*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 125*x^73 + 104*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 24*x^66 + 61*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 15*x^25 + 24*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 104*x^18 + 87*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 121*x^9 + 72*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 56*x^2 + 25*x + 24, x^93 + 74*x^91 + 28*x^90 + 11*x^89 + 76*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 116*x^82 + 67*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 21*x^73 + 68*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 124*x^66 + 101*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 55*x^25 + 60*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 4*x^18 + 111*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 49*x^9 + 52*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 12*x^2 + 33*x + 92, x^93 + 74*x^91 + 112*x^90 + 19*x^89 + 32*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 80*x^82 + 123*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 45*x^73 + 96*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 112*x^66 + 13*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 95*x^25 + 32*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 16*x^18 + 7*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 105*x^9 + 96*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 48*x^2 + 41*x + 32, x^93 + 74*x^91 + 116*x^90 + 123*x^89 + 20*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 124*x^82 + 19*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 101*x^73 + 92*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 84*x^66 + 85*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 103*x^25 + 36*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 44*x^18 + 127*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 65*x^9 + 108*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 4*x^2 + 81*x + 68, x^93 + 74*x^91 + 108*x^90 + 43*x^89 + 28*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 36*x^82 + 99*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 117*x^73 + 52*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 12*x^66 + 69*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 87*x^25 + 76*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 116*x^18 + 15*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 17*x^9 + 100*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 92*x^2 + x + 44, x^93 + 74*x^91 + 104*x^90 + 19*x^89 + 24*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 56*x^82 + 123*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 45*x^73 + 8*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 104*x^66 + 13*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 95*x^25 + 120*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 24*x^18 + 7*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 105*x^9 + 104*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 72*x^2 + 41*x + 120, x^93 + 74*x^91 + 112*x^90 + 19*x^89 + 64*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 16*x^82 + 59*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 45*x^73 + 64*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 48*x^66 + 77*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 95*x^25 + 64*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 80*x^18 + 71*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 105*x^9 + 64*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 112*x^2 + 105*x, x^93 + 74*x^91 + 80*x^90 + 99*x^89 + 16*x^88 + 68*x^87 + 32*x^86 + x^85 + 32*x^84 + 102*x^83 + 48*x^82 + 107*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 29*x^73 + 48*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 16*x^66 + 93*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 111*x^25 + 80*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 112*x^18 + 55*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 25*x^9 + 112*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 80*x^2 + 57*x + 16, x^93 + 74*x^91 + 116*x^90 + 123*x^89 + 52*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 124*x^82 + 19*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 101*x^73 + 60*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 84*x^66 + 85*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 103*x^25 + 68*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 44*x^18 + 127*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 65*x^9 + 76*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 4*x^2 + 81*x + 100, x^93 + 74*x^91 + 112*x^90 + 35*x^89 + 16*x^88 + 68*x^87 + 96*x^86 + x^85 + 32*x^84 + 102*x^83 + 16*x^82 + 43*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 93*x^73 + 48*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 48*x^66 + 29*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 47*x^25 + 80*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 80*x^18 + 119*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 89*x^9 + 112*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 112*x^2 + 121*x + 16, x^93 + 74*x^91 + 52*x^90 + 59*x^89 + 52*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 60*x^82 + 83*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 37*x^73 + 60*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 20*x^66 + 21*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 39*x^25 + 68*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 108*x^18 + 63*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + x^9 + 76*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 68*x^2 + 17*x + 100, x^93 + 74*x^91 + 108*x^90 + 123*x^89 + 108*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 36*x^82 + 19*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 101*x^73 + 36*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 12*x^66 + 85*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 103*x^25 + 92*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 116*x^18 + 127*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 65*x^9 + 20*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 92*x^2 + 81*x + 60, x^93 + 74*x^91 + 44*x^90 + 75*x^89 + 124*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 100*x^82 + 67*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 85*x^73 + 84*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 76*x^66 + 101*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 119*x^25 + 44*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 52*x^18 + 111*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 113*x^9 + 4*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 28*x^2 + 33*x + 12, x^93 + 74*x^91 + 48*x^90 + 83*x^89 + 32*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 16*x^82 + 59*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 109*x^73 + 96*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 48*x^66 + 77*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 31*x^25 + 32*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 80*x^18 + 71*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 41*x^9 + 96*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 112*x^2 + 105*x + 32, x^93 + 74*x^91 + 8*x^90 + 19*x^89 + 56*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 24*x^82 + 123*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 45*x^73 + 104*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 8*x^66 + 13*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 95*x^25 + 24*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 120*x^18 + 7*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 105*x^9 + 72*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 104*x^2 + 41*x + 24, x^93 + 74*x^91 + 84*x^90 + 75*x^89 + 36*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 92*x^82 + 3*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 85*x^73 + 12*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 116*x^66 + 37*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 119*x^25 + 116*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 12*x^18 + 47*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 113*x^9 + 92*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 36*x^2 + 97*x + 84, x^93 + 74*x^91 + 48*x^90 + 99*x^89 + 80*x^88 + 68*x^87 + 96*x^86 + x^85 + 32*x^84 + 102*x^83 + 80*x^82 + 107*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 29*x^73 + 112*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 112*x^66 + 93*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 111*x^25 + 16*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 16*x^18 + 55*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 25*x^9 + 48*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 48*x^2 + 57*x + 80, x^93 + 74*x^91 + 83*x^89 + 80*x^88 + 68*x^87 + 33*x^85 + 96*x^84 + 102*x^83 + 59*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 109*x^73 + 112*x^72 + 116*x^71 + 39*x^69 + 96*x^68 + 114*x^67 + 77*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 31*x^25 + 16*x^24 + 116*x^23 + 69*x^21 + 96*x^20 + 30*x^19 + 71*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 41*x^9 + 48*x^8 + 68*x^7 + 59*x^5 + 96*x^4 + 106*x^3 + 105*x + 16, x^93 + 74*x^91 + 76*x^90 + 11*x^89 + 28*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 4*x^82 + 67*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 21*x^73 + 52*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 44*x^66 + 101*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 55*x^25 + 76*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 84*x^18 + 111*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 49*x^9 + 100*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 124*x^2 + 33*x + 108, x^93 + 74*x^91 + 96*x^90 + 99*x^89 + 4*x^87 + 64*x^86 + 65*x^85 + 38*x^83 + 32*x^82 + 43*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 29*x^73 + 52*x^71 + 64*x^70 + 71*x^69 + 50*x^67 + 96*x^66 + 29*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 111*x^25 + 52*x^23 + 64*x^22 + 101*x^21 + 94*x^19 + 32*x^18 + 119*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 25*x^9 + 4*x^7 + 64*x^6 + 91*x^5 + 42*x^3 + 96*x^2 + 121*x, x^93 + 74*x^91 + 20*x^90 + 75*x^89 + 4*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 92*x^82 + 67*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 85*x^73 + 44*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 116*x^66 + 101*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 119*x^25 + 84*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 12*x^18 + 111*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 113*x^9 + 124*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 36*x^2 + 33*x + 116, x^93 + 74*x^91 + 20*x^90 + 107*x^89 + 36*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 28*x^82 + 99*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 53*x^73 + 12*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 52*x^66 + 69*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 23*x^25 + 116*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 76*x^18 + 15*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 81*x^9 + 92*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 100*x^2 + x + 84, x^93 + 74*x^91 + 24*x^90 + 19*x^89 + 72*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 8*x^82 + 59*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 45*x^73 + 24*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 88*x^66 + 77*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 95*x^25 + 104*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 40*x^18 + 71*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 105*x^9 + 56*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 120*x^2 + 105*x + 40, x^93 + 74*x^91 + 76*x^90 + 43*x^89 + 60*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 4*x^82 + 35*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 117*x^73 + 20*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 44*x^66 + 5*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 87*x^25 + 108*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 84*x^18 + 79*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 17*x^9 + 68*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 124*x^2 + 65*x + 12, x^93 + 74*x^91 + 80*x^90 + 35*x^89 + 112*x^88 + 68*x^87 + 32*x^86 + x^85 + 96*x^84 + 102*x^83 + 48*x^82 + 43*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 93*x^73 + 80*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 16*x^66 + 29*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 47*x^25 + 48*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 112*x^18 + 119*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 89*x^9 + 16*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 80*x^2 + 121*x + 112, x^93 + 74*x^91 + 56*x^90 + 3*x^89 + 88*x^88 + 4*x^87 + 16*x^86 + x^85 + 16*x^84 + 38*x^83 + 40*x^82 + 11*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 125*x^73 + 72*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 56*x^66 + 61*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 15*x^25 + 56*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 72*x^18 + 87*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 121*x^9 + 40*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 88*x^2 + 25*x + 56, x^93 + 74*x^91 + 60*x^90 + 107*x^89 + 108*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 84*x^82 + 99*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 53*x^73 + 36*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 28*x^66 + 69*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 23*x^25 + 92*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 100*x^18 + 15*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 81*x^9 + 20*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 44*x^2 + x + 124, x^93 + 74*x^91 + 84*x^90 + 75*x^89 + 4*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 92*x^82 + 3*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 85*x^73 + 44*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 116*x^66 + 37*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 119*x^25 + 84*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 12*x^18 + 47*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 113*x^9 + 124*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 36*x^2 + 97*x + 52, x^93 + 74*x^91 + 108*x^90 + 123*x^89 + 12*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 100*x^82 + 83*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 101*x^73 + 4*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 76*x^66 + 21*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 103*x^25 + 124*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 52*x^18 + 63*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 65*x^9 + 116*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 28*x^2 + 17*x + 28, x^93 + 74*x^91 + 24*x^90 + 83*x^89 + 8*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 8*x^82 + 123*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 109*x^73 + 88*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 88*x^66 + 13*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 31*x^25 + 40*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 40*x^18 + 7*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 41*x^9 + 120*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 120*x^2 + 41*x + 104, x^93 + 74*x^91 + 60*x^90 + 11*x^89 + 44*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 20*x^82 + 3*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 21*x^73 + 100*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 92*x^66 + 37*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 55*x^25 + 28*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 36*x^18 + 47*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 49*x^9 + 84*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 108*x^2 + 97*x + 124, x^93 + 74*x^91 + 56*x^90 + 83*x^89 + 72*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 104*x^82 + 123*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 109*x^73 + 24*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 120*x^66 + 13*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 31*x^25 + 104*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 8*x^18 + 7*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 41*x^9 + 56*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 24*x^2 + 41*x + 40, x^93 + 74*x^91 + 68*x^90 + 11*x^89 + 52*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 44*x^82 + 67*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 21*x^73 + 60*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 100*x^66 + 101*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 55*x^25 + 68*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 28*x^18 + 111*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 49*x^9 + 76*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 84*x^2 + 33*x + 36, x^93 + 74*x^91 + 32*x^90 + 3*x^89 + 64*x^88 + 4*x^87 + 64*x^86 + x^85 + 38*x^83 + 96*x^82 + 11*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 125*x^73 + 64*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 50*x^67 + 32*x^66 + 61*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 15*x^25 + 64*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 94*x^19 + 96*x^18 + 87*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 121*x^9 + 64*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 42*x^3 + 32*x^2 + 25*x + 64, x^93 + 74*x^91 + 44*x^90 + 59*x^89 + 44*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 100*x^82 + 83*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 37*x^73 + 100*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 76*x^66 + 21*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 39*x^25 + 28*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 52*x^18 + 63*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + x^9 + 84*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 28*x^2 + 17*x + 124, x^93 + 74*x^91 + 72*x^90 + 83*x^89 + 24*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 88*x^82 + 59*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 109*x^73 + 8*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 72*x^66 + 77*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 31*x^25 + 120*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 56*x^18 + 71*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 41*x^9 + 104*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 40*x^2 + 105*x + 120, x^93 + 74*x^91 + 4*x^90 + 11*x^89 + 20*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 108*x^82 + 67*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 21*x^73 + 92*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 36*x^66 + 101*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 55*x^25 + 36*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 92*x^18 + 111*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 49*x^9 + 108*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 20*x^2 + 33*x + 4, x^93 + 74*x^91 + 120*x^90 + 115*x^89 + 8*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 40*x^82 + 91*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 77*x^73 + 88*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 56*x^66 + 45*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 63*x^25 + 40*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 72*x^18 + 103*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 9*x^9 + 120*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 88*x^2 + 73*x + 104, x^93 + 74*x^91 + 40*x^90 + 35*x^89 + 8*x^88 + 68*x^87 + 112*x^86 + x^85 + 112*x^84 + 102*x^83 + 56*x^82 + 43*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 93*x^73 + 88*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 104*x^66 + 29*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 47*x^25 + 40*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 24*x^18 + 119*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 89*x^9 + 120*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 72*x^2 + 121*x + 104, x^93 + 74*x^91 + 44*x^90 + 11*x^89 + 60*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 100*x^82 + 3*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 21*x^73 + 20*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 76*x^66 + 37*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 55*x^25 + 108*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 52*x^18 + 47*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 49*x^9 + 68*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 28*x^2 + 97*x + 76, x^93 + 74*x^91 + 92*x^90 + 59*x^89 + 28*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 116*x^82 + 83*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 37*x^73 + 52*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 124*x^66 + 21*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 39*x^25 + 76*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 4*x^18 + 63*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + x^9 + 100*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 12*x^2 + 17*x + 44, x^93 + 74*x^91 + 100*x^90 + 59*x^89 + 100*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 76*x^82 + 83*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 37*x^73 + 76*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 68*x^66 + 21*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 39*x^25 + 52*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 60*x^18 + 63*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + x^9 + 28*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 52*x^2 + 17*x + 84, x^93 + 74*x^91 + 36*x^90 + 123*x^89 + 4*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 12*x^82 + 19*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 101*x^73 + 44*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 4*x^66 + 85*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 103*x^25 + 84*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 124*x^18 + 127*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 65*x^9 + 124*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 116*x^2 + 81*x + 116, x^93 + 74*x^91 + 32*x^90 + 51*x^89 + 112*x^88 + 4*x^87 + 33*x^85 + 96*x^84 + 38*x^83 + 32*x^82 + 27*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 13*x^73 + 80*x^72 + 52*x^71 + 39*x^69 + 96*x^68 + 50*x^67 + 96*x^66 + 109*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 127*x^25 + 48*x^24 + 52*x^23 + 69*x^21 + 96*x^20 + 94*x^19 + 32*x^18 + 39*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 73*x^9 + 16*x^8 + 4*x^7 + 59*x^5 + 96*x^4 + 42*x^3 + 96*x^2 + 9*x + 112, x^93 + 74*x^91 + 60*x^90 + 43*x^89 + 44*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 20*x^82 + 99*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 117*x^73 + 100*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 92*x^66 + 69*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 87*x^25 + 28*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 36*x^18 + 15*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 17*x^9 + 84*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 108*x^2 + x + 124, x^93 + 74*x^91 + 32*x^90 + 99*x^89 + 32*x^88 + 68*x^87 + x^85 + 102*x^83 + 32*x^82 + 107*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 29*x^73 + 96*x^72 + 116*x^71 + 7*x^69 + 114*x^67 + 96*x^66 + 93*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 111*x^25 + 32*x^24 + 116*x^23 + 37*x^21 + 30*x^19 + 32*x^18 + 55*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 25*x^9 + 96*x^8 + 68*x^7 + 27*x^5 + 106*x^3 + 96*x^2 + 57*x + 96, x^93 + 74*x^91 + 116*x^90 + 75*x^89 + 68*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 124*x^82 + 67*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 85*x^73 + 108*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 84*x^66 + 101*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 119*x^25 + 20*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 44*x^18 + 111*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 113*x^9 + 60*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 4*x^2 + 33*x + 52, x^93 + 74*x^91 + 124*x^90 + 107*x^89 + 12*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 84*x^82 + 35*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 53*x^73 + 4*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 28*x^66 + 5*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 23*x^25 + 124*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 100*x^18 + 79*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 81*x^9 + 116*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 44*x^2 + 65*x + 92, x^93 + 74*x^91 + 116*x^90 + 59*x^89 + 84*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 60*x^82 + 19*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 37*x^73 + 28*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 20*x^66 + 85*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 39*x^25 + 100*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 108*x^18 + 127*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + x^9 + 44*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 68*x^2 + 81*x + 68, x^93 + 74*x^91 + 44*x^90 + 43*x^89 + 92*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 36*x^82 + 35*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 117*x^73 + 116*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 12*x^66 + 5*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 87*x^25 + 12*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 116*x^18 + 79*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 17*x^9 + 36*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 92*x^2 + 65*x + 44, x^93 + 74*x^91 + 52*x^90 + 91*x^89 + 84*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 124*x^82 + 115*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 5*x^73 + 28*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 84*x^66 + 117*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 71*x^25 + 100*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 44*x^18 + 95*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 97*x^9 + 44*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 4*x^2 + 113*x + 68, x^93 + 74*x^91 + 116*x^90 + 43*x^89 + 68*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 124*x^82 + 99*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 117*x^73 + 108*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 84*x^66 + 69*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 87*x^25 + 20*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 44*x^18 + 15*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 17*x^9 + 60*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 4*x^2 + x + 52, x^93 + 74*x^91 + 124*x^90 + 123*x^89 + 60*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 20*x^82 + 83*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 101*x^73 + 20*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 92*x^66 + 21*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 103*x^25 + 108*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 36*x^18 + 63*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 65*x^9 + 68*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 108*x^2 + 17*x + 12, x^93 + 74*x^91 + 56*x^90 + 83*x^89 + 72*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 40*x^82 + 59*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 109*x^73 + 24*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 56*x^66 + 77*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 31*x^25 + 104*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 72*x^18 + 71*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 41*x^9 + 56*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 88*x^2 + 105*x + 104, x^93 + 74*x^91 + 112*x^90 + 115*x^89 + 64*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 102*x^83 + 80*x^82 + 27*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 77*x^73 + 64*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 114*x^67 + 112*x^66 + 109*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 63*x^25 + 64*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 30*x^19 + 16*x^18 + 39*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 9*x^9 + 64*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 106*x^3 + 48*x^2 + 9*x + 64, x^93 + 74*x^91 + 68*x^90 + 27*x^89 + 4*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 44*x^82 + 51*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 69*x^73 + 44*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 100*x^66 + 53*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 7*x^25 + 84*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 28*x^18 + 31*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 33*x^9 + 124*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 84*x^2 + 49*x + 52, x^93 + 74*x^91 + 68*x^90 + 43*x^89 + 116*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 44*x^82 + 35*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 117*x^73 + 124*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 100*x^66 + 5*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 87*x^25 + 4*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 28*x^18 + 79*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 17*x^9 + 12*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 84*x^2 + 65*x + 100, x^93 + 74*x^91 + 84*x^90 + 75*x^89 + 100*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 28*x^82 + 67*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 85*x^73 + 76*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 52*x^66 + 101*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 119*x^25 + 52*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 76*x^18 + 111*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 113*x^9 + 28*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 100*x^2 + 33*x + 84, x^93 + 74*x^91 + 88*x^90 + 115*x^89 + 72*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 72*x^82 + 91*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 77*x^73 + 24*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 24*x^66 + 45*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 63*x^25 + 104*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 104*x^18 + 103*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 9*x^9 + 56*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 56*x^2 + 73*x + 40, x^93 + 74*x^91 + 108*x^90 + 107*x^89 + 92*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 36*x^82 + 35*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 53*x^73 + 116*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 12*x^66 + 5*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 23*x^25 + 12*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 116*x^18 + 79*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 81*x^9 + 36*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 92*x^2 + 65*x + 108, x^93 + 74*x^91 + 16*x^90 + 35*x^89 + 48*x^88 + 68*x^87 + 32*x^86 + x^85 + 96*x^84 + 102*x^83 + 112*x^82 + 43*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 93*x^73 + 16*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 80*x^66 + 29*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 47*x^25 + 112*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 48*x^18 + 119*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 89*x^9 + 80*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 16*x^2 + 121*x + 48, x^93 + 74*x^91 + 52*x^90 + 75*x^89 + 100*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 124*x^82 + 3*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 85*x^73 + 76*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 84*x^66 + 37*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 119*x^25 + 52*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 44*x^18 + 47*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 113*x^9 + 28*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 4*x^2 + 97*x + 20, x^93 + 74*x^91 + 12*x^90 + 91*x^89 + 76*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 4*x^82 + 51*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 5*x^73 + 68*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 44*x^66 + 53*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 71*x^25 + 60*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 84*x^18 + 31*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 97*x^9 + 52*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 124*x^2 + 49*x + 28, x^93 + 74*x^91 + 40*x^90 + 19*x^89 + 56*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 120*x^82 + 123*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 45*x^73 + 104*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 40*x^66 + 13*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 95*x^25 + 24*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 88*x^18 + 7*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 105*x^9 + 72*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 8*x^2 + 41*x + 24, x^93 + 74*x^91 + 120*x^90 + 51*x^89 + 40*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 104*x^82 + 91*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 13*x^73 + 56*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 120*x^66 + 45*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 127*x^25 + 72*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 8*x^18 + 103*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 73*x^9 + 88*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 24*x^2 + 73*x + 72, x^93 + 74*x^91 + 51*x^89 + 112*x^88 + 68*x^87 + 97*x^85 + 32*x^84 + 102*x^83 + 91*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 13*x^73 + 80*x^72 + 116*x^71 + 103*x^69 + 32*x^68 + 114*x^67 + 45*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 127*x^25 + 48*x^24 + 116*x^23 + 5*x^21 + 32*x^20 + 30*x^19 + 103*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 73*x^9 + 16*x^8 + 68*x^7 + 123*x^5 + 32*x^4 + 106*x^3 + 73*x + 48, x^93 + 74*x^91 + 116*x^90 + 27*x^89 + 84*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 124*x^82 + 115*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 69*x^73 + 28*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 84*x^66 + 117*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 7*x^25 + 100*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 44*x^18 + 95*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 33*x^9 + 44*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 4*x^2 + 113*x + 4, x^93 + 74*x^91 + 124*x^90 + 27*x^89 + 92*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 84*x^82 + 115*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 69*x^73 + 116*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 28*x^66 + 117*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 7*x^25 + 12*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 100*x^18 + 95*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 33*x^9 + 36*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 44*x^2 + 113*x + 108, x^93 + 74*x^91 + 48*x^90 + 99*x^89 + 80*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 16*x^82 + 43*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 29*x^73 + 112*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 48*x^66 + 29*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 111*x^25 + 16*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 80*x^18 + 119*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 25*x^9 + 48*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 112*x^2 + 121*x + 16, x^93 + 74*x^91 + 35*x^89 + 64*x^88 + 4*x^87 + 65*x^85 + 38*x^83 + 107*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 93*x^73 + 64*x^72 + 52*x^71 + 71*x^69 + 50*x^67 + 93*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 47*x^25 + 64*x^24 + 52*x^23 + 101*x^21 + 94*x^19 + 55*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 89*x^9 + 64*x^8 + 4*x^7 + 91*x^5 + 42*x^3 + 57*x + 64, x^93 + 74*x^91 + 84*x^90 + 107*x^89 + 68*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 28*x^82 + 35*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 53*x^73 + 108*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 52*x^66 + 5*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 23*x^25 + 20*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 76*x^18 + 79*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 81*x^9 + 60*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 100*x^2 + 65*x + 52, x^93 + 74*x^91 + 32*x^90 + 51*x^89 + 48*x^88 + 4*x^87 + 33*x^85 + 96*x^84 + 38*x^83 + 32*x^82 + 27*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 13*x^73 + 16*x^72 + 52*x^71 + 39*x^69 + 96*x^68 + 50*x^67 + 96*x^66 + 109*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 127*x^25 + 112*x^24 + 52*x^23 + 69*x^21 + 96*x^20 + 94*x^19 + 32*x^18 + 39*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 73*x^9 + 80*x^8 + 4*x^7 + 59*x^5 + 96*x^4 + 42*x^3 + 96*x^2 + 9*x + 48, x^93 + 74*x^91 + 64*x^90 + 83*x^89 + 16*x^88 + 68*x^87 + 33*x^85 + 96*x^84 + 102*x^83 + 64*x^82 + 59*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 109*x^73 + 48*x^72 + 116*x^71 + 39*x^69 + 96*x^68 + 114*x^67 + 64*x^66 + 77*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 31*x^25 + 80*x^24 + 116*x^23 + 69*x^21 + 96*x^20 + 30*x^19 + 64*x^18 + 71*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 41*x^9 + 112*x^8 + 68*x^7 + 59*x^5 + 96*x^4 + 106*x^3 + 64*x^2 + 105*x + 80, x^93 + 74*x^91 + 16*x^90 + 83*x^89 + 68*x^87 + 96*x^86 + 33*x^85 + 102*x^83 + 48*x^82 + 59*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 109*x^73 + 116*x^71 + 96*x^70 + 39*x^69 + 114*x^67 + 16*x^66 + 77*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 31*x^25 + 116*x^23 + 96*x^22 + 69*x^21 + 30*x^19 + 112*x^18 + 71*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 41*x^9 + 68*x^7 + 96*x^6 + 59*x^5 + 106*x^3 + 80*x^2 + 105*x, x^93 + 74*x^91 + 48*x^90 + 3*x^89 + 16*x^88 + 4*x^87 + 32*x^86 + x^85 + 96*x^84 + 38*x^83 + 16*x^82 + 11*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 125*x^73 + 48*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 48*x^66 + 61*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 15*x^25 + 80*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 80*x^18 + 87*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 121*x^9 + 112*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 112*x^2 + 25*x + 80, x^93 + 74*x^91 + 28*x^90 + 43*x^89 + 12*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 52*x^82 + 99*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 117*x^73 + 4*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 60*x^66 + 69*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 87*x^25 + 124*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 68*x^18 + 15*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 17*x^9 + 116*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 76*x^2 + x + 92, x^93 + 74*x^91 + 96*x^90 + 35*x^89 + 96*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 38*x^83 + 32*x^82 + 107*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 93*x^73 + 32*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 50*x^67 + 96*x^66 + 93*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 47*x^25 + 96*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 94*x^19 + 32*x^18 + 55*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 89*x^9 + 32*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 42*x^3 + 96*x^2 + 57*x + 96, x^93 + 74*x^91 + 88*x^90 + 3*x^89 + 120*x^88 + 4*x^87 + 80*x^86 + x^85 + 80*x^84 + 38*x^83 + 8*x^82 + 11*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 125*x^73 + 40*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 88*x^66 + 61*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 15*x^25 + 88*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 40*x^18 + 87*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 121*x^9 + 8*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 120*x^2 + 25*x + 88, x^93 + 74*x^91 + 20*x^90 + 123*x^89 + 116*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 28*x^82 + 83*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 101*x^73 + 124*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 52*x^66 + 21*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 103*x^25 + 4*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 76*x^18 + 63*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 65*x^9 + 12*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 100*x^2 + 17*x + 100, x^93 + 74*x^91 + 72*x^90 + 3*x^89 + 8*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 24*x^82 + 75*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 125*x^73 + 88*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 8*x^66 + 125*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 15*x^25 + 40*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 120*x^18 + 23*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 121*x^9 + 120*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 104*x^2 + 89*x + 104, x^93 + 74*x^91 + 72*x^90 + 19*x^89 + 56*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 88*x^82 + 123*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 45*x^73 + 104*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 72*x^66 + 13*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 95*x^25 + 24*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 56*x^18 + 7*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 105*x^9 + 72*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 40*x^2 + 41*x + 24, x^93 + 74*x^91 + 60*x^90 + 123*x^89 + 124*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 20*x^82 + 19*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 101*x^73 + 84*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 92*x^66 + 85*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 103*x^25 + 44*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 36*x^18 + 127*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 65*x^9 + 4*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 108*x^2 + 81*x + 12, x^93 + 74*x^91 + 100*x^90 + 75*x^89 + 116*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 76*x^82 + 67*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 85*x^73 + 124*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 68*x^66 + 101*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 119*x^25 + 4*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 60*x^18 + 111*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 113*x^9 + 12*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 52*x^2 + 33*x + 36, x^93 + 74*x^91 + 32*x^90 + 115*x^89 + 80*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 102*x^83 + 96*x^82 + 27*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 77*x^73 + 112*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 114*x^67 + 32*x^66 + 109*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 63*x^25 + 16*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 30*x^19 + 96*x^18 + 39*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 9*x^9 + 48*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 106*x^3 + 32*x^2 + 9*x + 16, x^93 + 74*x^91 + 4*x^90 + 27*x^89 + 68*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 44*x^82 + 115*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 69*x^73 + 108*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 100*x^66 + 117*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 7*x^25 + 20*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 28*x^18 + 95*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 33*x^9 + 60*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 84*x^2 + 113*x + 52, x^93 + 74*x^91 + 60*x^90 + 107*x^89 + 44*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 20*x^82 + 35*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 53*x^73 + 100*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 92*x^66 + 5*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 23*x^25 + 28*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 36*x^18 + 79*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 81*x^9 + 84*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 108*x^2 + 65*x + 124, x^93 + 74*x^91 + 88*x^90 + 19*x^89 + 72*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 72*x^82 + 59*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 45*x^73 + 24*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 24*x^66 + 77*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 95*x^25 + 104*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 104*x^18 + 71*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 105*x^9 + 56*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 56*x^2 + 105*x + 40, x^93 + 74*x^91 + 64*x^90 + 99*x^89 + 68*x^87 + 64*x^86 + x^85 + 64*x^84 + 102*x^83 + 107*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 29*x^73 + 116*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 114*x^67 + 93*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 111*x^25 + 116*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 30*x^19 + 55*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 25*x^9 + 68*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 106*x^3 + 57*x + 64, x^93 + 74*x^91 + 60*x^90 + 43*x^89 + 44*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 84*x^82 + 35*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 117*x^73 + 100*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 28*x^66 + 5*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 87*x^25 + 28*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 100*x^18 + 79*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 17*x^9 + 84*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 44*x^2 + 65*x + 60, x^93 + 74*x^91 + 88*x^90 + 83*x^89 + 72*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 72*x^82 + 123*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 109*x^73 + 24*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 24*x^66 + 13*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 31*x^25 + 104*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 104*x^18 + 7*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 41*x^9 + 56*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 56*x^2 + 41*x + 40, x^93 + 74*x^91 + 116*x^90 + 91*x^89 + 84*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 60*x^82 + 115*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 5*x^73 + 28*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 20*x^66 + 117*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 71*x^25 + 100*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 108*x^18 + 95*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 97*x^9 + 44*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 68*x^2 + 113*x + 68, x^93 + 74*x^91 + 48*x^90 + 99*x^89 + 16*x^88 + 68*x^87 + 96*x^86 + x^85 + 32*x^84 + 102*x^83 + 80*x^82 + 107*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 29*x^73 + 48*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 112*x^66 + 93*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 111*x^25 + 80*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 16*x^18 + 55*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 25*x^9 + 112*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 48*x^2 + 57*x + 16, x^93 + 74*x^91 + 20*x^90 + 91*x^89 + 116*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 28*x^82 + 115*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 5*x^73 + 124*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 52*x^66 + 117*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 71*x^25 + 4*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 76*x^18 + 95*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 97*x^9 + 12*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 100*x^2 + 113*x + 100, x^93 + 74*x^91 + 92*x^90 + 91*x^89 + 92*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 52*x^82 + 115*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 5*x^73 + 116*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 60*x^66 + 117*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 71*x^25 + 12*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 68*x^18 + 95*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 97*x^9 + 36*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 76*x^2 + 113*x + 44, x^93 + 74*x^91 + 48*x^90 + 67*x^89 + 48*x^88 + 4*x^87 + 32*x^86 + x^85 + 32*x^84 + 38*x^83 + 16*x^82 + 75*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 61*x^73 + 16*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 48*x^66 + 125*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 79*x^25 + 112*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 80*x^18 + 23*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 57*x^9 + 80*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 112*x^2 + 89*x + 112, x^93 + 74*x^91 + 120*x^90 + 19*x^89 + 104*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 104*x^82 + 123*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 45*x^73 + 120*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 120*x^66 + 13*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 95*x^25 + 8*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 8*x^18 + 7*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 105*x^9 + 24*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 24*x^2 + 41*x + 8, x^93 + 74*x^91 + 124*x^90 + 75*x^89 + 44*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 84*x^82 + 67*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 85*x^73 + 100*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 28*x^66 + 101*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 119*x^25 + 28*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 100*x^18 + 111*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 113*x^9 + 84*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 44*x^2 + 33*x + 124, x^93 + 74*x^91 + 80*x^90 + 51*x^89 + 4*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 48*x^82 + 27*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 13*x^73 + 52*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 16*x^66 + 109*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 127*x^25 + 52*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 112*x^18 + 39*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 73*x^9 + 4*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 80*x^2 + 9*x + 64, x^93 + 74*x^91 + 60*x^90 + 11*x^89 + 108*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 84*x^82 + 67*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 21*x^73 + 36*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 28*x^66 + 101*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 55*x^25 + 92*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 100*x^18 + 111*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 49*x^9 + 20*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 44*x^2 + 33*x + 124, x^93 + 74*x^91 + 112*x^90 + 3*x^89 + 80*x^88 + 4*x^87 + 32*x^86 + x^85 + 96*x^84 + 38*x^83 + 80*x^82 + 11*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 125*x^73 + 112*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 112*x^66 + 61*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 15*x^25 + 16*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 16*x^18 + 87*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 121*x^9 + 48*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 48*x^2 + 25*x + 16, x^93 + 74*x^91 + 124*x^90 + 11*x^89 + 12*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 20*x^82 + 67*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 21*x^73 + 4*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 92*x^66 + 101*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 55*x^25 + 124*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 36*x^18 + 111*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 49*x^9 + 116*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 108*x^2 + 33*x + 28, x^93 + 74*x^91 + 68*x^90 + 91*x^89 + 36*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 44*x^82 + 115*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 5*x^73 + 12*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 100*x^66 + 117*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 71*x^25 + 116*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 28*x^18 + 95*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 97*x^9 + 92*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 84*x^2 + 113*x + 84, x^93 + 74*x^91 + 104*x^90 + 83*x^89 + 120*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 120*x^82 + 123*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 109*x^73 + 40*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 40*x^66 + 13*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 31*x^25 + 88*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 88*x^18 + 7*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 41*x^9 + 8*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 8*x^2 + 41*x + 24, x^93 + 74*x^91 + 84*x^90 + 59*x^89 + 116*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 28*x^82 + 83*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 37*x^73 + 124*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 52*x^66 + 21*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 39*x^25 + 4*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 76*x^18 + 63*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + x^9 + 12*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 100*x^2 + 17*x + 36, x^93 + 74*x^91 + 24*x^90 + 99*x^89 + 88*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 72*x^82 + 43*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 29*x^73 + 72*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 24*x^66 + 29*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 111*x^25 + 56*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 104*x^18 + 119*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 25*x^9 + 40*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 56*x^2 + 121*x + 56, x^93 + 74*x^91 + 44*x^90 + 11*x^89 + 92*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 36*x^82 + 67*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 21*x^73 + 116*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 12*x^66 + 101*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 55*x^25 + 12*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 116*x^18 + 111*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 49*x^9 + 36*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 92*x^2 + 33*x + 44, x^93 + 74*x^91 + 76*x^90 + 11*x^89 + 28*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 68*x^82 + 3*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 21*x^73 + 52*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 108*x^66 + 37*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 55*x^25 + 76*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 20*x^18 + 47*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 49*x^9 + 100*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 60*x^2 + 97*x + 44, x^93 + 74*x^91 + 20*x^90 + 43*x^89 + 36*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 92*x^82 + 99*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 117*x^73 + 12*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 116*x^66 + 69*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 87*x^25 + 116*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 12*x^18 + 15*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 17*x^9 + 92*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 36*x^2 + x + 20, x^93 + 74*x^91 + 88*x^90 + 115*x^89 + 104*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 8*x^82 + 27*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 77*x^73 + 120*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 88*x^66 + 109*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 63*x^25 + 8*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 40*x^18 + 39*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 9*x^9 + 24*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 120*x^2 + 9*x + 8, x^93 + 74*x^91 + 96*x^90 + 83*x^89 + 48*x^88 + 4*x^87 + 97*x^85 + 96*x^84 + 38*x^83 + 96*x^82 + 123*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 109*x^73 + 16*x^72 + 52*x^71 + 103*x^69 + 96*x^68 + 50*x^67 + 32*x^66 + 13*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 31*x^25 + 112*x^24 + 52*x^23 + 5*x^21 + 96*x^20 + 94*x^19 + 96*x^18 + 7*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 41*x^9 + 80*x^8 + 4*x^7 + 123*x^5 + 96*x^4 + 42*x^3 + 32*x^2 + 41*x + 48, x^93 + 74*x^91 + 76*x^90 + 107*x^89 + 92*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 4*x^82 + 99*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 53*x^73 + 116*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 44*x^66 + 69*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 23*x^25 + 12*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 84*x^18 + 15*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 81*x^9 + 36*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 124*x^2 + x + 44, x^93 + 74*x^91 + 44*x^90 + 27*x^89 + 76*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 36*x^82 + 51*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 69*x^73 + 68*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 12*x^66 + 53*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 7*x^25 + 60*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 116*x^18 + 31*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 33*x^9 + 52*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 92*x^2 + 49*x + 92, x^93 + 74*x^91 + 96*x^90 + 83*x^89 + 48*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 102*x^83 + 32*x^82 + 59*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 109*x^73 + 16*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 114*x^67 + 96*x^66 + 77*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 31*x^25 + 112*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 30*x^19 + 32*x^18 + 71*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 41*x^9 + 80*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 106*x^3 + 96*x^2 + 105*x + 112, x^93 + 74*x^91 + 120*x^90 + 51*x^89 + 104*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 40*x^82 + 27*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 13*x^73 + 120*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 56*x^66 + 109*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 127*x^25 + 8*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 72*x^18 + 39*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 73*x^9 + 24*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 88*x^2 + 9*x + 72, x^93 + 74*x^91 + 4*x^90 + 11*x^89 + 116*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 108*x^82 + 67*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 21*x^73 + 124*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 36*x^66 + 101*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 55*x^25 + 4*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 92*x^18 + 111*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 49*x^9 + 12*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 20*x^2 + 33*x + 100, x^93 + 74*x^91 + 104*x^90 + 83*x^89 + 88*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 56*x^82 + 59*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 109*x^73 + 72*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 104*x^66 + 77*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 31*x^25 + 56*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 24*x^18 + 71*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 41*x^9 + 40*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 72*x^2 + 105*x + 56, x^93 + 74*x^91 + 52*x^90 + 27*x^89 + 84*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 124*x^82 + 51*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 69*x^73 + 28*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 84*x^66 + 53*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 7*x^25 + 100*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 44*x^18 + 31*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 33*x^9 + 44*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 4*x^2 + 49*x + 68, x^93 + 74*x^91 + 120*x^90 + 83*x^89 + 8*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 104*x^82 + 59*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 109*x^73 + 88*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 120*x^66 + 77*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 31*x^25 + 40*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 8*x^18 + 71*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 41*x^9 + 120*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 24*x^2 + 105*x + 40, x^93 + 74*x^91 + 120*x^90 + 99*x^89 + 24*x^88 + 68*x^87 + 80*x^86 + x^85 + 80*x^84 + 102*x^83 + 40*x^82 + 107*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 29*x^73 + 8*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 56*x^66 + 93*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 111*x^25 + 120*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 72*x^18 + 55*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 25*x^9 + 104*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 88*x^2 + 57*x + 56, x^93 + 74*x^91 + 67*x^89 + 64*x^88 + 4*x^87 + x^85 + 38*x^83 + 75*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 61*x^73 + 64*x^72 + 52*x^71 + 7*x^69 + 50*x^67 + 125*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 79*x^25 + 64*x^24 + 52*x^23 + 37*x^21 + 94*x^19 + 23*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 57*x^9 + 64*x^8 + 4*x^7 + 27*x^5 + 42*x^3 + 89*x + 64, x^93 + 74*x^91 + 68*x^90 + 123*x^89 + 36*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 44*x^82 + 83*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 101*x^73 + 12*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 100*x^66 + 21*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 103*x^25 + 116*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 28*x^18 + 63*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 65*x^9 + 92*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 84*x^2 + 17*x + 84, x^93 + 74*x^91 + 52*x^90 + 11*x^89 + 36*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 124*x^82 + 67*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 21*x^73 + 12*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 84*x^66 + 101*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 55*x^25 + 116*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 44*x^18 + 111*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 49*x^9 + 92*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 4*x^2 + 33*x + 84, x^93 + 74*x^91 + 112*x^90 + 83*x^89 + 4*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 16*x^82 + 123*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 109*x^73 + 52*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 48*x^66 + 13*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 31*x^25 + 52*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 80*x^18 + 7*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 41*x^9 + 4*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 112*x^2 + 41*x + 64, x^93 + 74*x^91 + 124*x^90 + 107*x^89 + 76*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 20*x^82 + 99*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 53*x^73 + 68*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 92*x^66 + 69*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 23*x^25 + 60*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 36*x^18 + 15*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 81*x^9 + 52*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 108*x^2 + x + 92, x^93 + 74*x^91 + 112*x^90 + 99*x^89 + 80*x^88 + 68*x^87 + 96*x^86 + x^85 + 32*x^84 + 102*x^83 + 16*x^82 + 107*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 29*x^73 + 112*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 48*x^66 + 93*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 111*x^25 + 16*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 80*x^18 + 55*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 25*x^9 + 48*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 112*x^2 + 57*x + 80, x^93 + 74*x^91 + 12*x^90 + 91*x^89 + 44*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 4*x^82 + 51*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 5*x^73 + 100*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 44*x^66 + 53*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 71*x^25 + 28*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 84*x^18 + 31*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 97*x^9 + 84*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 124*x^2 + 49*x + 124, x^93 + 74*x^91 + 99*x^89 + 68*x^87 + 64*x^86 + x^85 + 64*x^84 + 102*x^83 + 64*x^82 + 107*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 29*x^73 + 116*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 114*x^67 + 64*x^66 + 93*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 111*x^25 + 116*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 30*x^19 + 64*x^18 + 55*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 25*x^9 + 68*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 106*x^3 + 64*x^2 + 57*x + 64, x^93 + 74*x^91 + 16*x^90 + 83*x^89 + 64*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 112*x^82 + 123*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 109*x^73 + 64*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 80*x^66 + 13*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 31*x^25 + 64*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 48*x^18 + 7*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 41*x^9 + 64*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 16*x^2 + 41*x, x^93 + 74*x^91 + 112*x^90 + 35*x^89 + 112*x^88 + 68*x^87 + 96*x^86 + x^85 + 96*x^84 + 102*x^83 + 16*x^82 + 43*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 93*x^73 + 80*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 48*x^66 + 29*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 47*x^25 + 48*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 80*x^18 + 119*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 89*x^9 + 16*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 112*x^2 + 121*x + 112, x^93 + 74*x^91 + 120*x^90 + 35*x^89 + 120*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 104*x^82 + 107*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 93*x^73 + 40*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 120*x^66 + 93*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 47*x^25 + 88*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 8*x^18 + 55*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 89*x^9 + 8*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 24*x^2 + 57*x + 88, x^93 + 74*x^91 + 60*x^90 + 59*x^89 + 60*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 84*x^82 + 19*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 37*x^73 + 20*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 28*x^66 + 85*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 39*x^25 + 108*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 100*x^18 + 127*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + x^9 + 68*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 44*x^2 + 81*x + 12, x^93 + 74*x^91 + 68*x^90 + 43*x^89 + 20*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 44*x^82 + 35*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 117*x^73 + 92*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 100*x^66 + 5*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 87*x^25 + 36*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 28*x^18 + 79*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 17*x^9 + 108*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 84*x^2 + 65*x + 4, x^93 + 74*x^91 + 100*x^90 + 123*x^89 + 4*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 12*x^82 + 83*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 101*x^73 + 44*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 4*x^66 + 21*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 103*x^25 + 84*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 124*x^18 + 63*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 65*x^9 + 124*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 116*x^2 + 17*x + 52, x^93 + 74*x^91 + 64*x^90 + 3*x^89 + 32*x^88 + 4*x^87 + x^85 + 64*x^84 + 38*x^83 + 64*x^82 + 11*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 125*x^73 + 96*x^72 + 52*x^71 + 7*x^69 + 64*x^68 + 50*x^67 + 64*x^66 + 61*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 15*x^25 + 32*x^24 + 52*x^23 + 37*x^21 + 64*x^20 + 94*x^19 + 64*x^18 + 87*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 121*x^9 + 96*x^8 + 4*x^7 + 27*x^5 + 64*x^4 + 42*x^3 + 64*x^2 + 25*x + 32, x^93 + 74*x^91 + 96*x^90 + 99*x^89 + 32*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 38*x^83 + 32*x^82 + 43*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 29*x^73 + 96*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 50*x^67 + 96*x^66 + 29*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 111*x^25 + 32*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 94*x^19 + 32*x^18 + 119*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 25*x^9 + 96*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 42*x^3 + 96*x^2 + 121*x + 32, x^93 + 74*x^91 + 40*x^90 + 99*x^89 + 72*x^88 + 68*x^87 + 112*x^86 + x^85 + 112*x^84 + 102*x^83 + 56*x^82 + 107*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 29*x^73 + 24*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 104*x^66 + 93*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 111*x^25 + 104*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 24*x^18 + 55*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 25*x^9 + 56*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 72*x^2 + 57*x + 40, x^93 + 74*x^91 + 100*x^90 + 123*x^89 + 4*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 76*x^82 + 19*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 101*x^73 + 44*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 68*x^66 + 85*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 103*x^25 + 84*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 60*x^18 + 127*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 65*x^9 + 124*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 52*x^2 + 81*x + 116, x^93 + 74*x^91 + 16*x^90 + 67*x^89 + 112*x^88 + 4*x^87 + 96*x^86 + x^85 + 32*x^84 + 38*x^83 + 48*x^82 + 75*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 61*x^73 + 80*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 16*x^66 + 125*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 79*x^25 + 48*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 112*x^18 + 23*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 57*x^9 + 16*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 80*x^2 + 89*x + 48, x^93 + 74*x^91 + 92*x^90 + 91*x^89 + 28*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 52*x^82 + 115*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 5*x^73 + 52*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 60*x^66 + 117*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 71*x^25 + 76*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 68*x^18 + 95*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 97*x^9 + 100*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 76*x^2 + 113*x + 108, x^93 + 74*x^91 + 124*x^90 + 43*x^89 + 44*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 84*x^82 + 99*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 117*x^73 + 100*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 28*x^66 + 69*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 87*x^25 + 28*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 100*x^18 + 15*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 17*x^9 + 84*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 44*x^2 + x + 124, x^93 + 74*x^91 + 32*x^90 + 83*x^89 + 112*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 102*x^83 + 96*x^82 + 59*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 109*x^73 + 80*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 114*x^67 + 32*x^66 + 77*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 31*x^25 + 48*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 30*x^19 + 96*x^18 + 71*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 41*x^9 + 16*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 106*x^3 + 32*x^2 + 105*x + 48, x^93 + 74*x^91 + 72*x^90 + 3*x^89 + 104*x^88 + 4*x^87 + 112*x^86 + x^85 + 112*x^84 + 38*x^83 + 88*x^82 + 11*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 125*x^73 + 120*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 72*x^66 + 61*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 15*x^25 + 8*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 56*x^18 + 87*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 121*x^9 + 24*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 40*x^2 + 25*x + 8, x^93 + 74*x^91 + 24*x^90 + 3*x^89 + 56*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 8*x^82 + 75*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 125*x^73 + 104*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 88*x^66 + 125*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 15*x^25 + 24*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 40*x^18 + 23*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 121*x^9 + 72*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 120*x^2 + 89*x + 88, x^93 + 74*x^91 + 116*x^90 + 27*x^89 + 52*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 124*x^82 + 115*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 69*x^73 + 60*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 84*x^66 + 117*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 7*x^25 + 68*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 44*x^18 + 95*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 33*x^9 + 76*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 4*x^2 + 113*x + 100, x^93 + 74*x^91 + 120*x^90 + 99*x^89 + 56*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 104*x^82 + 43*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 29*x^73 + 104*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 120*x^66 + 29*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 111*x^25 + 24*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 8*x^18 + 119*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 25*x^9 + 72*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 24*x^2 + 121*x + 24, x^93 + 74*x^91 + 108*x^90 + 11*x^89 + 60*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 100*x^82 + 67*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 21*x^73 + 20*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 76*x^66 + 101*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 55*x^25 + 108*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 52*x^18 + 111*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 49*x^9 + 68*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 28*x^2 + 33*x + 12, x^93 + 74*x^91 + 112*x^90 + 99*x^89 + 112*x^88 + 68*x^87 + 96*x^86 + x^85 + 96*x^84 + 102*x^83 + 16*x^82 + 107*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 29*x^73 + 80*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 48*x^66 + 93*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 111*x^25 + 48*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 80*x^18 + 55*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 25*x^9 + 16*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 112*x^2 + 57*x + 112, x^93 + 74*x^91 + 68*x^90 + 123*x^89 + 100*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 44*x^82 + 83*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 101*x^73 + 76*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 100*x^66 + 21*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 103*x^25 + 52*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 28*x^18 + 63*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 65*x^9 + 28*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 84*x^2 + 17*x + 20, x^93 + 74*x^91 + 92*x^90 + 75*x^89 + 44*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 52*x^82 + 3*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 85*x^73 + 100*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 60*x^66 + 37*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 119*x^25 + 28*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 68*x^18 + 47*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 113*x^9 + 84*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 76*x^2 + 97*x + 60, x^93 + 74*x^91 + 48*x^90 + 35*x^89 + 16*x^88 + 68*x^87 + 96*x^86 + x^85 + 32*x^84 + 102*x^83 + 80*x^82 + 43*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 93*x^73 + 48*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 112*x^66 + 29*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 47*x^25 + 80*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 16*x^18 + 119*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 89*x^9 + 112*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 48*x^2 + 121*x + 16, x^93 + 74*x^91 + 64*x^90 + 51*x^89 + 16*x^88 + 68*x^87 + 97*x^85 + 96*x^84 + 102*x^83 + 64*x^82 + 91*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 13*x^73 + 48*x^72 + 116*x^71 + 103*x^69 + 96*x^68 + 114*x^67 + 64*x^66 + 45*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 127*x^25 + 80*x^24 + 116*x^23 + 5*x^21 + 96*x^20 + 30*x^19 + 64*x^18 + 103*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 73*x^9 + 112*x^8 + 68*x^7 + 123*x^5 + 96*x^4 + 106*x^3 + 64*x^2 + 73*x + 80, x^93 + 74*x^91 + 96*x^90 + 35*x^89 + 4*x^87 + 64*x^86 + 65*x^85 + 38*x^83 + 32*x^82 + 107*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 93*x^73 + 52*x^71 + 64*x^70 + 71*x^69 + 50*x^67 + 96*x^66 + 93*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 47*x^25 + 52*x^23 + 64*x^22 + 101*x^21 + 94*x^19 + 32*x^18 + 55*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 89*x^9 + 4*x^7 + 64*x^6 + 91*x^5 + 42*x^3 + 96*x^2 + 57*x, x^93 + 74*x^91 + 104*x^90 + 115*x^89 + 56*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 120*x^82 + 91*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 77*x^73 + 104*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 40*x^66 + 45*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 63*x^25 + 24*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 88*x^18 + 103*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 9*x^9 + 72*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 8*x^2 + 73*x + 88, x^93 + 74*x^91 + 108*x^90 + 11*x^89 + 28*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 100*x^82 + 67*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 21*x^73 + 52*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 76*x^66 + 101*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 55*x^25 + 76*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 52*x^18 + 111*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 49*x^9 + 100*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 28*x^2 + 33*x + 108, x^93 + 74*x^91 + 52*x^90 + 43*x^89 + 68*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 124*x^82 + 35*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 117*x^73 + 108*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 84*x^66 + 5*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 87*x^25 + 20*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 44*x^18 + 79*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 17*x^9 + 60*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 4*x^2 + 65*x + 116, x^93 + 74*x^91 + 56*x^90 + 3*x^89 + 120*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 104*x^82 + 75*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 125*x^73 + 40*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 120*x^66 + 125*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 15*x^25 + 88*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 8*x^18 + 23*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 121*x^9 + 8*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 24*x^2 + 89*x + 24, x^93 + 74*x^91 + 52*x^90 + 123*x^89 + 52*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 124*x^82 + 83*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 101*x^73 + 60*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 84*x^66 + 21*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 103*x^25 + 68*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 44*x^18 + 63*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 65*x^9 + 76*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 4*x^2 + 17*x + 36, x^93 + 74*x^91 + 64*x^90 + 67*x^89 + 64*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 102*x^83 + 11*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 61*x^73 + 64*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 114*x^67 + 61*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 79*x^25 + 64*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 30*x^19 + 87*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 57*x^9 + 64*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 106*x^3 + 25*x, x^93 + 74*x^91 + 8*x^90 + 51*x^89 + 120*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 24*x^82 + 91*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 13*x^73 + 40*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 8*x^66 + 45*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 127*x^25 + 88*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 120*x^18 + 103*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 73*x^9 + 8*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 104*x^2 + 73*x + 88, x^93 + 74*x^91 + 100*x^90 + 91*x^89 + 100*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 12*x^82 + 115*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 5*x^73 + 76*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 4*x^66 + 117*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 71*x^25 + 52*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 124*x^18 + 95*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 97*x^9 + 28*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 116*x^2 + 113*x + 20, x^93 + 74*x^91 + 108*x^90 + 107*x^89 + 28*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 100*x^82 + 99*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 53*x^73 + 52*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 76*x^66 + 69*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 23*x^25 + 76*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 52*x^18 + 15*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 81*x^9 + 100*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 28*x^2 + x + 108, x^93 + 74*x^91 + 96*x^90 + 115*x^89 + 112*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 102*x^83 + 32*x^82 + 27*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 77*x^73 + 80*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 114*x^67 + 96*x^66 + 109*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 63*x^25 + 48*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 30*x^19 + 32*x^18 + 39*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 9*x^9 + 16*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 106*x^3 + 96*x^2 + 9*x + 48, x^93 + 74*x^91 + 36*x^90 + 123*x^89 + 68*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 12*x^82 + 19*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 101*x^73 + 108*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 4*x^66 + 85*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 103*x^25 + 20*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 124*x^18 + 127*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 65*x^9 + 60*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 116*x^2 + 81*x + 52, x^93 + 74*x^91 + 67*x^89 + 64*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 102*x^83 + 64*x^82 + 11*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 61*x^73 + 64*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 114*x^67 + 64*x^66 + 61*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 79*x^25 + 64*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 30*x^19 + 64*x^18 + 87*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 57*x^9 + 64*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 106*x^3 + 64*x^2 + 25*x, x^93 + 74*x^91 + 44*x^90 + 43*x^89 + 92*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 100*x^82 + 99*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 117*x^73 + 116*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 76*x^66 + 69*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 87*x^25 + 12*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 52*x^18 + 15*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 17*x^9 + 36*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 28*x^2 + x + 108, x^93 + 74*x^91 + 72*x^90 + 83*x^89 + 24*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 24*x^82 + 123*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 109*x^73 + 8*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 8*x^66 + 13*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 31*x^25 + 120*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 120*x^18 + 7*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 41*x^9 + 104*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 104*x^2 + 41*x + 56, x^93 + 74*x^91 + 92*x^90 + 75*x^89 + 108*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 116*x^82 + 67*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 85*x^73 + 36*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 124*x^66 + 101*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 119*x^25 + 92*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 4*x^18 + 111*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 113*x^9 + 20*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 12*x^2 + 33*x + 60, x^93 + 74*x^91 + 80*x^90 + 19*x^89 + 64*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 102*x^83 + 112*x^82 + 123*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 45*x^73 + 64*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 114*x^67 + 80*x^66 + 13*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 95*x^25 + 64*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 30*x^19 + 48*x^18 + 7*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 105*x^9 + 64*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 106*x^3 + 16*x^2 + 41*x + 64, x^93 + 74*x^91 + 24*x^90 + 83*x^89 + 104*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 72*x^82 + 59*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 109*x^73 + 120*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 24*x^66 + 77*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 31*x^25 + 8*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 104*x^18 + 71*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 41*x^9 + 24*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 56*x^2 + 105*x + 8, x^93 + 74*x^91 + 116*x^90 + 27*x^89 + 84*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 60*x^82 + 51*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 69*x^73 + 28*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 20*x^66 + 53*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 7*x^25 + 100*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 108*x^18 + 31*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 33*x^9 + 44*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 68*x^2 + 49*x + 68, x^93 + 74*x^91 + 76*x^90 + 75*x^89 + 60*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 68*x^82 + 67*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 85*x^73 + 20*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 108*x^66 + 101*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 119*x^25 + 108*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 20*x^18 + 111*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 113*x^9 + 68*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 60*x^2 + 33*x + 76, x^93 + 74*x^91 + 48*x^90 + 67*x^89 + 16*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 80*x^82 + 11*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 61*x^73 + 48*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 112*x^66 + 61*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 79*x^25 + 80*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 16*x^18 + 87*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 57*x^9 + 112*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 48*x^2 + 25*x + 16, x^93 + 74*x^91 + 20*x^90 + 11*x^89 + 68*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 28*x^82 + 67*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 21*x^73 + 108*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 52*x^66 + 101*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 55*x^25 + 20*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 76*x^18 + 111*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 49*x^9 + 60*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 100*x^2 + 33*x + 116, x^93 + 74*x^91 + 124*x^90 + 11*x^89 + 76*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 84*x^82 + 3*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 21*x^73 + 68*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 28*x^66 + 37*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 55*x^25 + 60*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 100*x^18 + 47*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 49*x^9 + 52*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 44*x^2 + 97*x + 28, x^93 + 74*x^91 + 76*x^90 + 91*x^89 + 108*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 4*x^82 + 115*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 5*x^73 + 36*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 44*x^66 + 117*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 71*x^25 + 92*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 84*x^18 + 95*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 97*x^9 + 20*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 124*x^2 + 113*x + 124, x^93 + 74*x^91 + 48*x^90 + 19*x^89 + 32*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 16*x^82 + 123*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 45*x^73 + 96*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 48*x^66 + 13*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 95*x^25 + 32*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 80*x^18 + 7*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 105*x^9 + 96*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 112*x^2 + 41*x + 32, x^93 + 74*x^91 + 88*x^90 + 67*x^89 + 120*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 72*x^82 + 11*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 61*x^73 + 40*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 24*x^66 + 61*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 79*x^25 + 88*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 104*x^18 + 87*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 57*x^9 + 8*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 56*x^2 + 25*x + 24, x^93 + 74*x^91 + 84*x^90 + 123*x^89 + 116*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 92*x^82 + 83*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 101*x^73 + 124*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 116*x^66 + 21*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 103*x^25 + 4*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 12*x^18 + 63*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 65*x^9 + 12*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 36*x^2 + 17*x + 100, x^93 + 74*x^91 + 120*x^90 + 3*x^89 + 24*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 40*x^82 + 75*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 125*x^73 + 8*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 56*x^66 + 125*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 15*x^25 + 120*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 72*x^18 + 23*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 121*x^9 + 104*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 88*x^2 + 89*x + 56, x^93 + 74*x^91 + 84*x^90 + 43*x^89 + 100*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 92*x^82 + 35*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 117*x^73 + 76*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 116*x^66 + 5*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 87*x^25 + 52*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 12*x^18 + 79*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 17*x^9 + 28*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 36*x^2 + 65*x + 20, x^93 + 74*x^91 + 92*x^90 + 123*x^89 + 60*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 52*x^82 + 83*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 101*x^73 + 20*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 60*x^66 + 21*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 103*x^25 + 108*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 68*x^18 + 63*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 65*x^9 + 68*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 76*x^2 + 17*x + 12, x^93 + 74*x^91 + 108*x^90 + 59*x^89 + 12*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 100*x^82 + 19*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 37*x^73 + 4*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 76*x^66 + 85*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 39*x^25 + 124*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 52*x^18 + 127*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + x^9 + 116*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 28*x^2 + 81*x + 28, x^93 + 74*x^91 + 116*x^90 + 75*x^89 + 36*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 124*x^82 + 67*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 85*x^73 + 12*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 84*x^66 + 101*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 119*x^25 + 116*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 44*x^18 + 111*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 113*x^9 + 92*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 4*x^2 + 33*x + 20, x^93 + 74*x^91 + 44*x^90 + 43*x^89 + 124*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 36*x^82 + 35*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 117*x^73 + 84*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 12*x^66 + 5*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 87*x^25 + 44*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 116*x^18 + 79*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 17*x^9 + 4*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 92*x^2 + 65*x + 76, x^93 + 74*x^91 + 68*x^90 + 91*x^89 + 68*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 108*x^82 + 51*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 5*x^73 + 108*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 36*x^66 + 53*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 71*x^25 + 20*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 92*x^18 + 31*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 97*x^9 + 60*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 20*x^2 + 49*x + 52, x^93 + 74*x^91 + 120*x^90 + 83*x^89 + 8*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 40*x^82 + 123*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 109*x^73 + 88*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 56*x^66 + 13*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 31*x^25 + 40*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 72*x^18 + 7*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 41*x^9 + 120*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 88*x^2 + 41*x + 104, x^93 + 74*x^91 + 88*x^90 + 83*x^89 + 104*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 72*x^82 + 123*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 109*x^73 + 120*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 24*x^66 + 13*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 31*x^25 + 8*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 104*x^18 + 7*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 41*x^9 + 24*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 56*x^2 + 41*x + 72, x^93 + 74*x^91 + 12*x^90 + 59*x^89 + 12*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 68*x^82 + 19*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 37*x^73 + 4*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 108*x^66 + 85*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 39*x^25 + 124*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 20*x^18 + 127*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + x^9 + 116*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 60*x^2 + 81*x + 28, x^93 + 74*x^91 + 72*x^90 + 35*x^89 + 72*x^88 + 68*x^87 + 48*x^86 + x^85 + 112*x^84 + 102*x^83 + 24*x^82 + 43*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 93*x^73 + 24*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 8*x^66 + 29*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 47*x^25 + 104*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 120*x^18 + 119*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 89*x^9 + 56*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 104*x^2 + 121*x + 40, x^93 + 74*x^91 + 48*x^90 + 115*x^89 + 64*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 102*x^83 + 16*x^82 + 27*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 77*x^73 + 64*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 114*x^67 + 48*x^66 + 109*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 63*x^25 + 64*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 30*x^19 + 80*x^18 + 39*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 9*x^9 + 64*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 106*x^3 + 112*x^2 + 9*x + 64, x^93 + 74*x^91 + 40*x^90 + 35*x^89 + 104*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 120*x^82 + 107*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 93*x^73 + 120*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 40*x^66 + 93*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 47*x^25 + 8*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 88*x^18 + 55*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 89*x^9 + 24*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 8*x^2 + 57*x + 8, x^93 + 74*x^91 + 84*x^90 + 123*x^89 + 84*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 28*x^82 + 19*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 101*x^73 + 28*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 52*x^66 + 85*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 103*x^25 + 100*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 76*x^18 + 127*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 65*x^9 + 44*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 100*x^2 + 81*x + 4, x^93 + 74*x^91 + 24*x^90 + 99*x^89 + 56*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 72*x^82 + 43*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 29*x^73 + 104*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 24*x^66 + 29*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 111*x^25 + 24*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 104*x^18 + 119*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 25*x^9 + 72*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 56*x^2 + 121*x + 24, x^93 + 74*x^91 + 4*x^90 + 11*x^89 + 84*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 44*x^82 + 3*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 21*x^73 + 28*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 100*x^66 + 37*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 55*x^25 + 100*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 28*x^18 + 47*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 49*x^9 + 44*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 84*x^2 + 97*x + 4, x^93 + 74*x^91 + 48*x^90 + 115*x^89 + 96*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 16*x^82 + 27*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 77*x^73 + 32*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 48*x^66 + 109*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 63*x^25 + 96*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 80*x^18 + 39*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 9*x^9 + 32*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 112*x^2 + 9*x + 96, x^93 + 74*x^91 + 32*x^90 + 19*x^89 + 48*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 102*x^83 + 96*x^82 + 123*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 45*x^73 + 16*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 114*x^67 + 32*x^66 + 13*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 95*x^25 + 112*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 30*x^19 + 96*x^18 + 7*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 105*x^9 + 80*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 106*x^3 + 32*x^2 + 41*x + 112, x^93 + 74*x^91 + 92*x^90 + 107*x^89 + 108*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 52*x^82 + 99*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 53*x^73 + 36*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 60*x^66 + 69*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 23*x^25 + 92*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 68*x^18 + 15*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 81*x^9 + 20*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 76*x^2 + x + 124, x^93 + 74*x^91 + 124*x^90 + 11*x^89 + 12*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 84*x^82 + 3*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 21*x^73 + 4*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 28*x^66 + 37*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 55*x^25 + 124*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 100*x^18 + 47*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 49*x^9 + 116*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 44*x^2 + 97*x + 92, x^93 + 74*x^91 + 20*x^90 + 123*x^89 + 84*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 28*x^82 + 83*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 101*x^73 + 28*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 52*x^66 + 21*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 103*x^25 + 100*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 76*x^18 + 63*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 65*x^9 + 44*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 100*x^2 + 17*x + 68, x^93 + 74*x^91 + 96*x^90 + 67*x^89 + 4*x^87 + 64*x^86 + x^85 + 38*x^83 + 32*x^82 + 75*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 61*x^73 + 52*x^71 + 64*x^70 + 7*x^69 + 50*x^67 + 96*x^66 + 125*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 79*x^25 + 52*x^23 + 64*x^22 + 37*x^21 + 94*x^19 + 32*x^18 + 23*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 57*x^9 + 4*x^7 + 64*x^6 + 27*x^5 + 42*x^3 + 96*x^2 + 89*x, x^93 + 74*x^91 + 19*x^89 + 16*x^88 + 68*x^87 + 33*x^85 + 96*x^84 + 102*x^83 + 123*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 45*x^73 + 48*x^72 + 116*x^71 + 39*x^69 + 96*x^68 + 114*x^67 + 13*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 95*x^25 + 80*x^24 + 116*x^23 + 69*x^21 + 96*x^20 + 30*x^19 + 7*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 105*x^9 + 112*x^8 + 68*x^7 + 59*x^5 + 96*x^4 + 106*x^3 + 41*x + 80, x^93 + 74*x^91 + 20*x^90 + 123*x^89 + 52*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 92*x^82 + 19*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 101*x^73 + 60*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 116*x^66 + 85*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 103*x^25 + 68*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 12*x^18 + 127*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 65*x^9 + 76*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 36*x^2 + 81*x + 100, x^93 + 74*x^91 + 72*x^90 + 51*x^89 + 120*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 88*x^82 + 91*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 13*x^73 + 40*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 72*x^66 + 45*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 127*x^25 + 88*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 56*x^18 + 103*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 73*x^9 + 8*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 40*x^2 + 73*x + 88, x^93 + 74*x^91 + 20*x^90 + 107*x^89 + 68*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 92*x^82 + 35*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 53*x^73 + 108*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 116*x^66 + 5*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 23*x^25 + 20*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 12*x^18 + 79*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 81*x^9 + 60*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 36*x^2 + 65*x + 52, x^93 + 74*x^91 + 100*x^90 + 123*x^89 + 36*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 76*x^82 + 19*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 101*x^73 + 12*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 68*x^66 + 85*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 103*x^25 + 116*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 60*x^18 + 127*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 65*x^9 + 92*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 52*x^2 + 81*x + 20, x^93 + 74*x^91 + 108*x^90 + 43*x^89 + 92*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 36*x^82 + 99*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 117*x^73 + 116*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 12*x^66 + 69*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 87*x^25 + 12*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 116*x^18 + 15*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 17*x^9 + 36*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 92*x^2 + x + 108, x^93 + 74*x^91 + 72*x^90 + 99*x^89 + 72*x^88 + 68*x^87 + 48*x^86 + x^85 + 112*x^84 + 102*x^83 + 24*x^82 + 107*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 29*x^73 + 24*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 8*x^66 + 93*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 111*x^25 + 104*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 120*x^18 + 55*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 25*x^9 + 56*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 104*x^2 + 57*x + 40, x^93 + 74*x^91 + 4*x^90 + 123*x^89 + 4*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 108*x^82 + 83*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 101*x^73 + 44*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 36*x^66 + 21*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 103*x^25 + 84*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 92*x^18 + 63*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 65*x^9 + 124*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 20*x^2 + 17*x + 52, x^93 + 74*x^91 + 44*x^90 + 107*x^89 + 92*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 36*x^82 + 99*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 53*x^73 + 116*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 12*x^66 + 69*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 23*x^25 + 12*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 116*x^18 + 15*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 81*x^9 + 36*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 92*x^2 + x + 44, x^93 + 74*x^91 + 116*x^90 + 59*x^89 + 116*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 60*x^82 + 19*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 37*x^73 + 124*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 20*x^66 + 85*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 39*x^25 + 4*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 108*x^18 + 127*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + x^9 + 12*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 68*x^2 + 81*x + 100, x^93 + 74*x^91 + 72*x^90 + 3*x^89 + 72*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 24*x^82 + 75*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 125*x^73 + 24*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 8*x^66 + 125*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 15*x^25 + 104*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 120*x^18 + 23*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 121*x^9 + 56*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 104*x^2 + 89*x + 40, x^93 + 74*x^91 + 28*x^90 + 27*x^89 + 124*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 116*x^82 + 51*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 69*x^73 + 84*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 124*x^66 + 53*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 7*x^25 + 44*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 4*x^18 + 31*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 33*x^9 + 4*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 12*x^2 + 49*x + 76, x^93 + 74*x^91 + 20*x^90 + 59*x^89 + 84*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 92*x^82 + 83*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 37*x^73 + 28*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 116*x^66 + 21*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 39*x^25 + 100*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 12*x^18 + 63*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + x^9 + 44*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 36*x^2 + 17*x + 4, x^93 + 74*x^91 + 40*x^90 + 51*x^89 + 24*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 120*x^82 + 91*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 13*x^73 + 8*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 40*x^66 + 45*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 127*x^25 + 120*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 88*x^18 + 103*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 73*x^9 + 104*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 8*x^2 + 73*x + 120, x^93 + 74*x^91 + 84*x^90 + 91*x^89 + 84*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 28*x^82 + 51*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 5*x^73 + 28*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 52*x^66 + 53*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 71*x^25 + 100*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 76*x^18 + 31*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 97*x^9 + 44*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 100*x^2 + 49*x + 4, x^93 + 74*x^91 + 80*x^90 + 19*x^89 + 68*x^87 + 96*x^86 + 33*x^85 + 102*x^83 + 112*x^82 + 123*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 45*x^73 + 116*x^71 + 96*x^70 + 39*x^69 + 114*x^67 + 80*x^66 + 13*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 95*x^25 + 116*x^23 + 96*x^22 + 69*x^21 + 30*x^19 + 48*x^18 + 7*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 105*x^9 + 68*x^7 + 96*x^6 + 59*x^5 + 106*x^3 + 16*x^2 + 41*x, x^93 + 74*x^91 + 104*x^90 + 83*x^89 + 56*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 56*x^82 + 59*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 109*x^73 + 104*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 104*x^66 + 77*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 31*x^25 + 24*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 24*x^18 + 71*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 41*x^9 + 72*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 72*x^2 + 105*x + 24, x^93 + 74*x^91 + 92*x^90 + 59*x^89 + 92*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 52*x^82 + 19*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 37*x^73 + 116*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 60*x^66 + 85*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 39*x^25 + 12*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 68*x^18 + 127*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + x^9 + 36*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 76*x^2 + 81*x + 44, x^93 + 74*x^91 + 96*x^90 + 3*x^89 + 32*x^88 + 68*x^87 + 65*x^85 + 102*x^83 + 96*x^82 + 75*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 125*x^73 + 96*x^72 + 116*x^71 + 71*x^69 + 114*x^67 + 32*x^66 + 125*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 15*x^25 + 32*x^24 + 116*x^23 + 101*x^21 + 30*x^19 + 96*x^18 + 23*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 121*x^9 + 96*x^8 + 68*x^7 + 91*x^5 + 106*x^3 + 32*x^2 + 89*x + 96, x^93 + 74*x^91 + 76*x^90 + 27*x^89 + 12*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 68*x^82 + 115*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 69*x^73 + 4*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 108*x^66 + 117*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 7*x^25 + 124*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 20*x^18 + 95*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 33*x^9 + 116*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 60*x^2 + 113*x + 92, x^93 + 74*x^91 + 84*x^90 + 11*x^89 + 68*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 28*x^82 + 3*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 21*x^73 + 108*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 52*x^66 + 37*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 55*x^25 + 20*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 76*x^18 + 47*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 49*x^9 + 60*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 100*x^2 + 97*x + 52, x^93 + 74*x^91 + 32*x^90 + 35*x^89 + 68*x^87 + x^85 + 64*x^84 + 102*x^83 + 32*x^82 + 43*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 93*x^73 + 116*x^71 + 7*x^69 + 64*x^68 + 114*x^67 + 96*x^66 + 29*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 47*x^25 + 116*x^23 + 37*x^21 + 64*x^20 + 30*x^19 + 32*x^18 + 119*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 89*x^9 + 68*x^7 + 27*x^5 + 64*x^4 + 106*x^3 + 96*x^2 + 121*x + 64, x^93 + 74*x^91 + 64*x^90 + 83*x^89 + 80*x^88 + 68*x^87 + 33*x^85 + 96*x^84 + 102*x^83 + 64*x^82 + 59*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 109*x^73 + 112*x^72 + 116*x^71 + 39*x^69 + 96*x^68 + 114*x^67 + 64*x^66 + 77*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 31*x^25 + 16*x^24 + 116*x^23 + 69*x^21 + 96*x^20 + 30*x^19 + 64*x^18 + 71*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 41*x^9 + 48*x^8 + 68*x^7 + 59*x^5 + 96*x^4 + 106*x^3 + 64*x^2 + 105*x + 16, x^93 + 74*x^91 + 96*x^90 + 99*x^89 + 96*x^88 + 68*x^87 + x^85 + 102*x^83 + 96*x^82 + 107*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 29*x^73 + 32*x^72 + 116*x^71 + 7*x^69 + 114*x^67 + 32*x^66 + 93*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 111*x^25 + 96*x^24 + 116*x^23 + 37*x^21 + 30*x^19 + 96*x^18 + 55*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 25*x^9 + 32*x^8 + 68*x^7 + 27*x^5 + 106*x^3 + 32*x^2 + 57*x + 32, x^93 + 74*x^91 + 92*x^90 + 11*x^89 + 12*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 52*x^82 + 67*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 21*x^73 + 4*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 60*x^66 + 101*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 55*x^25 + 124*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 68*x^18 + 111*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 49*x^9 + 116*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 76*x^2 + 33*x + 28, x^93 + 74*x^91 + 8*x^90 + 51*x^89 + 24*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 24*x^82 + 91*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 13*x^73 + 8*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 8*x^66 + 45*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 127*x^25 + 120*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 120*x^18 + 103*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 73*x^9 + 104*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 104*x^2 + 73*x + 120, x^93 + 74*x^91 + 84*x^90 + 91*x^89 + 52*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 28*x^82 + 51*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 5*x^73 + 60*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 52*x^66 + 53*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 71*x^25 + 68*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 76*x^18 + 31*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 97*x^9 + 76*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 100*x^2 + 49*x + 100, x^93 + 74*x^91 + 56*x^90 + 3*x^89 + 24*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 104*x^82 + 75*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 125*x^73 + 8*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 120*x^66 + 125*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 15*x^25 + 120*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 8*x^18 + 23*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 121*x^9 + 104*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 24*x^2 + 89*x + 56, x^93 + 74*x^91 + 100*x^90 + 91*x^89 + 68*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 76*x^82 + 51*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 5*x^73 + 108*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 68*x^66 + 53*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 71*x^25 + 20*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 60*x^18 + 31*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 97*x^9 + 60*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 52*x^2 + 49*x + 52, x^93 + 74*x^91 + 124*x^90 + 75*x^89 + 44*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 20*x^82 + 3*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 85*x^73 + 100*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 92*x^66 + 37*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 119*x^25 + 28*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 36*x^18 + 47*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 113*x^9 + 84*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 108*x^2 + 97*x + 60, x^93 + 74*x^91 + 100*x^90 + 107*x^89 + 84*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 76*x^82 + 35*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 53*x^73 + 28*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 68*x^66 + 5*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 23*x^25 + 100*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 60*x^18 + 79*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 81*x^9 + 44*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 52*x^2 + 65*x + 4, x^93 + 74*x^91 + 12*x^90 + 107*x^89 + 28*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 4*x^82 + 35*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 53*x^73 + 52*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 44*x^66 + 5*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 23*x^25 + 76*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 84*x^18 + 79*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 81*x^9 + 100*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 124*x^2 + 65*x + 44, x^93 + 74*x^91 + 8*x^90 + 67*x^89 + 40*x^88 + 4*x^87 + 112*x^86 + x^85 + 112*x^84 + 38*x^83 + 24*x^82 + 75*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 61*x^73 + 56*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 8*x^66 + 125*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 79*x^25 + 72*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 120*x^18 + 23*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 57*x^9 + 88*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 104*x^2 + 89*x + 72, x^93 + 74*x^91 + 68*x^90 + 123*x^89 + 68*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 108*x^82 + 19*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 101*x^73 + 108*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 36*x^66 + 85*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 103*x^25 + 20*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 92*x^18 + 127*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 65*x^9 + 60*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 20*x^2 + 81*x + 52, x^93 + 74*x^91 + 120*x^90 + 19*x^89 + 72*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 104*x^82 + 123*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 45*x^73 + 24*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 120*x^66 + 13*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 95*x^25 + 104*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 8*x^18 + 7*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 105*x^9 + 56*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 24*x^2 + 41*x + 104, x^93 + 74*x^91 + 108*x^90 + 107*x^89 + 124*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 36*x^82 + 35*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 53*x^73 + 84*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 12*x^66 + 5*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 23*x^25 + 44*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 116*x^18 + 79*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 81*x^9 + 4*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 92*x^2 + 65*x + 12, x^93 + 74*x^91 + 32*x^90 + 3*x^89 + 64*x^88 + 68*x^87 + 65*x^85 + 64*x^84 + 102*x^83 + 32*x^82 + 75*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 125*x^73 + 64*x^72 + 116*x^71 + 71*x^69 + 64*x^68 + 114*x^67 + 96*x^66 + 125*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 15*x^25 + 64*x^24 + 116*x^23 + 101*x^21 + 64*x^20 + 30*x^19 + 32*x^18 + 23*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 121*x^9 + 64*x^8 + 68*x^7 + 91*x^5 + 64*x^4 + 106*x^3 + 96*x^2 + 89*x, x^93 + 74*x^91 + 16*x^90 + 115*x^89 + 32*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 38*x^83 + 112*x^82 + 91*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 77*x^73 + 96*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 50*x^67 + 80*x^66 + 45*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 63*x^25 + 32*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 94*x^19 + 48*x^18 + 103*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 9*x^9 + 96*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 42*x^3 + 16*x^2 + 73*x + 96, x^93 + 74*x^91 + 4*x^90 + 75*x^89 + 52*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 108*x^82 + 3*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 85*x^73 + 60*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 36*x^66 + 37*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 119*x^25 + 68*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 92*x^18 + 47*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 113*x^9 + 76*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 20*x^2 + 97*x + 36, x^93 + 74*x^91 + 84*x^90 + 91*x^89 + 20*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 28*x^82 + 51*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 5*x^73 + 92*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 52*x^66 + 53*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 71*x^25 + 36*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 76*x^18 + 31*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 97*x^9 + 108*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 100*x^2 + 49*x + 68, x^93 + 74*x^91 + 88*x^90 + 99*x^89 + 56*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 8*x^82 + 43*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 29*x^73 + 104*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 88*x^66 + 29*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 111*x^25 + 24*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 40*x^18 + 119*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 25*x^9 + 72*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 120*x^2 + 121*x + 24, x^93 + 74*x^91 + 4*x^90 + 75*x^89 + 84*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 44*x^82 + 67*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 85*x^73 + 28*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 100*x^66 + 101*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 119*x^25 + 100*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 28*x^18 + 111*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 113*x^9 + 44*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 84*x^2 + 33*x + 4, x^93 + 74*x^91 + 28*x^90 + 27*x^89 + 28*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 116*x^82 + 51*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 69*x^73 + 52*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 124*x^66 + 53*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 7*x^25 + 76*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 4*x^18 + 31*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 33*x^9 + 100*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 12*x^2 + 49*x + 108, x^93 + 74*x^91 + 112*x^90 + 67*x^89 + 112*x^88 + 4*x^87 + 32*x^86 + x^85 + 32*x^84 + 38*x^83 + 80*x^82 + 75*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 61*x^73 + 80*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 112*x^66 + 125*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 79*x^25 + 48*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 16*x^18 + 23*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 57*x^9 + 16*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 48*x^2 + 89*x + 48, x^93 + 74*x^91 + 4*x^90 + 123*x^89 + 68*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 108*x^82 + 83*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 101*x^73 + 108*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 36*x^66 + 21*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 103*x^25 + 20*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 92*x^18 + 63*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 65*x^9 + 60*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 20*x^2 + 17*x + 116, x^93 + 74*x^91 + 36*x^90 + 27*x^89 + 36*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 12*x^82 + 115*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 69*x^73 + 12*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 4*x^66 + 117*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 7*x^25 + 116*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 124*x^18 + 95*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 33*x^9 + 92*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 116*x^2 + 113*x + 20, x^93 + 74*x^91 + 76*x^90 + 27*x^89 + 108*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 4*x^82 + 51*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 69*x^73 + 36*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 44*x^66 + 53*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 7*x^25 + 92*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 84*x^18 + 31*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 33*x^9 + 20*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 124*x^2 + 49*x + 124, x^93 + 74*x^91 + 44*x^90 + 75*x^89 + 92*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 36*x^82 + 3*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 85*x^73 + 116*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 12*x^66 + 37*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 119*x^25 + 12*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 116*x^18 + 47*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 113*x^9 + 36*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 92*x^2 + 97*x + 44, x^93 + 74*x^91 + 56*x^90 + 99*x^89 + 24*x^88 + 68*x^87 + 80*x^86 + x^85 + 80*x^84 + 102*x^83 + 104*x^82 + 107*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 29*x^73 + 8*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 120*x^66 + 93*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 111*x^25 + 120*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 8*x^18 + 55*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 25*x^9 + 104*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 24*x^2 + 57*x + 56, x^93 + 74*x^91 + 40*x^90 + 115*x^89 + 56*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 120*x^82 + 27*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 77*x^73 + 104*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 40*x^66 + 109*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 63*x^25 + 24*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 88*x^18 + 39*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 9*x^9 + 72*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 8*x^2 + 9*x + 24, x^93 + 74*x^91 + 48*x^90 + 35*x^89 + 80*x^88 + 68*x^87 + 96*x^86 + x^85 + 32*x^84 + 102*x^83 + 80*x^82 + 43*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 93*x^73 + 112*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 112*x^66 + 29*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 47*x^25 + 16*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 16*x^18 + 119*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 89*x^9 + 48*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 48*x^2 + 121*x + 80, x^93 + 74*x^91 + 52*x^90 + 59*x^89 + 116*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 124*x^82 + 19*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 37*x^73 + 124*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 84*x^66 + 85*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 39*x^25 + 4*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 44*x^18 + 127*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + x^9 + 12*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 4*x^2 + 81*x + 100, x^93 + 74*x^91 + 56*x^90 + 3*x^89 + 88*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 104*x^82 + 75*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 125*x^73 + 72*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 120*x^66 + 125*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 15*x^25 + 56*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 8*x^18 + 23*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 121*x^9 + 40*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 24*x^2 + 89*x + 120, x^93 + 74*x^91 + 116*x^90 + 11*x^89 + 68*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 60*x^82 + 67*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 21*x^73 + 108*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 20*x^66 + 101*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 55*x^25 + 20*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 108*x^18 + 111*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 49*x^9 + 60*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 68*x^2 + 33*x + 116, x^93 + 74*x^91 + 36*x^90 + 27*x^89 + 36*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 76*x^82 + 51*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 69*x^73 + 12*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 68*x^66 + 53*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 7*x^25 + 116*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 60*x^18 + 31*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 33*x^9 + 92*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 52*x^2 + 49*x + 84, x^93 + 74*x^91 + 24*x^90 + 51*x^89 + 104*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 8*x^82 + 27*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 13*x^73 + 120*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 88*x^66 + 109*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 127*x^25 + 8*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 40*x^18 + 39*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 73*x^9 + 24*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 120*x^2 + 9*x + 72, x^93 + 74*x^91 + 56*x^90 + 67*x^89 + 24*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 104*x^82 + 11*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 61*x^73 + 8*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 120*x^66 + 61*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 79*x^25 + 120*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 8*x^18 + 87*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 57*x^9 + 104*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 24*x^2 + 25*x + 56, x^93 + 74*x^91 + 4*x^90 + 75*x^89 + 52*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 44*x^82 + 67*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 85*x^73 + 60*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 100*x^66 + 101*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 119*x^25 + 68*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 28*x^18 + 111*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 113*x^9 + 76*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 84*x^2 + 33*x + 100, x^93 + 74*x^91 + 68*x^90 + 75*x^89 + 116*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 44*x^82 + 3*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 85*x^73 + 124*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 100*x^66 + 37*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 119*x^25 + 4*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 28*x^18 + 47*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 113*x^9 + 12*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 84*x^2 + 97*x + 100, x^93 + 74*x^91 + 115*x^89 + 80*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 38*x^83 + 64*x^82 + 91*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 77*x^73 + 112*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 50*x^67 + 64*x^66 + 45*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 63*x^25 + 16*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 94*x^19 + 64*x^18 + 103*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 9*x^9 + 48*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 42*x^3 + 64*x^2 + 73*x + 80, x^93 + 74*x^91 + 92*x^90 + 75*x^89 + 108*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 52*x^82 + 3*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 85*x^73 + 36*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 60*x^66 + 37*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 119*x^25 + 92*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 68*x^18 + 47*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 113*x^9 + 20*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 76*x^2 + 97*x + 124, x^93 + 74*x^91 + 80*x^90 + 19*x^89 + 32*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 38*x^83 + 48*x^82 + 59*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 45*x^73 + 96*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 50*x^67 + 16*x^66 + 77*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 95*x^25 + 32*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 94*x^19 + 112*x^18 + 71*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 105*x^9 + 96*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 42*x^3 + 80*x^2 + 105*x + 96, x^93 + 74*x^91 + 24*x^90 + 19*x^89 + 8*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 72*x^82 + 123*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 45*x^73 + 88*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 24*x^66 + 13*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 95*x^25 + 40*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 104*x^18 + 7*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 105*x^9 + 120*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 56*x^2 + 41*x + 40, x^93 + 74*x^91 + 88*x^90 + 51*x^89 + 40*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 72*x^82 + 27*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 13*x^73 + 56*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 24*x^66 + 109*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 127*x^25 + 72*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 104*x^18 + 39*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 73*x^9 + 88*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 56*x^2 + 9*x + 8, x^93 + 74*x^91 + 100*x^90 + 43*x^89 + 116*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 12*x^82 + 35*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 117*x^73 + 124*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 4*x^66 + 5*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 87*x^25 + 4*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 124*x^18 + 79*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 17*x^9 + 12*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 116*x^2 + 65*x + 100, x^93 + 74*x^91 + 12*x^90 + 123*x^89 + 108*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 68*x^82 + 83*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 101*x^73 + 36*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 108*x^66 + 21*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 103*x^25 + 92*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 20*x^18 + 63*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 65*x^9 + 20*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 60*x^2 + 17*x + 124, x^93 + 74*x^91 + 96*x^90 + 35*x^89 + 68*x^87 + x^85 + 64*x^84 + 102*x^83 + 96*x^82 + 43*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 93*x^73 + 116*x^71 + 7*x^69 + 64*x^68 + 114*x^67 + 32*x^66 + 29*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 47*x^25 + 116*x^23 + 37*x^21 + 64*x^20 + 30*x^19 + 96*x^18 + 119*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 89*x^9 + 68*x^7 + 27*x^5 + 64*x^4 + 106*x^3 + 32*x^2 + 121*x + 64, x^93 + 74*x^91 + 104*x^90 + 51*x^89 + 24*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 56*x^82 + 91*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 13*x^73 + 8*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 104*x^66 + 45*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 127*x^25 + 120*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 24*x^18 + 103*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 73*x^9 + 104*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 72*x^2 + 73*x + 120, x^93 + 74*x^91 + 4*x^90 + 11*x^89 + 52*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 44*x^82 + 3*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 21*x^73 + 60*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 100*x^66 + 37*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 55*x^25 + 68*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 28*x^18 + 47*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 49*x^9 + 76*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 84*x^2 + 97*x + 100, x^93 + 74*x^91 + 12*x^90 + 43*x^89 + 92*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 68*x^82 + 35*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 117*x^73 + 116*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 108*x^66 + 5*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 87*x^25 + 12*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 20*x^18 + 79*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 17*x^9 + 36*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 60*x^2 + 65*x + 44, x^93 + 74*x^91 + 84*x^90 + 75*x^89 + 68*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 28*x^82 + 67*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 85*x^73 + 108*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 52*x^66 + 101*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 119*x^25 + 20*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 76*x^18 + 111*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 113*x^9 + 60*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 100*x^2 + 33*x + 52, x^93 + 74*x^91 + 16*x^90 + 99*x^89 + 80*x^88 + 68*x^87 + 32*x^86 + x^85 + 32*x^84 + 102*x^83 + 112*x^82 + 107*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 29*x^73 + 112*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 80*x^66 + 93*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 111*x^25 + 16*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 48*x^18 + 55*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 25*x^9 + 48*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 16*x^2 + 57*x + 80, x^93 + 74*x^91 + 100*x^90 + 43*x^89 + 52*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 12*x^82 + 35*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 117*x^73 + 60*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 4*x^66 + 5*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 87*x^25 + 68*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 124*x^18 + 79*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 17*x^9 + 76*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 116*x^2 + 65*x + 36, x^93 + 74*x^91 + 20*x^90 + 75*x^89 + 68*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 28*x^82 + 3*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 85*x^73 + 108*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 52*x^66 + 37*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 119*x^25 + 20*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 76*x^18 + 47*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 113*x^9 + 60*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 100*x^2 + 97*x + 116, x^93 + 74*x^91 + 84*x^90 + 11*x^89 + 68*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 92*x^82 + 67*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 21*x^73 + 108*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 116*x^66 + 101*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 55*x^25 + 20*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 12*x^18 + 111*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 49*x^9 + 60*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 36*x^2 + 33*x + 116, x^93 + 74*x^91 + 24*x^90 + 99*x^89 + 120*x^88 + 68*x^87 + 16*x^86 + x^85 + 16*x^84 + 102*x^83 + 8*x^82 + 107*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 29*x^73 + 40*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 88*x^66 + 93*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 111*x^25 + 88*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 40*x^18 + 55*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 25*x^9 + 8*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 120*x^2 + 57*x + 24, x^93 + 74*x^91 + 44*x^90 + 123*x^89 + 108*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 100*x^82 + 19*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 101*x^73 + 36*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 76*x^66 + 85*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 103*x^25 + 92*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 52*x^18 + 127*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 65*x^9 + 20*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 28*x^2 + 81*x + 60, x^93 + 74*x^91 + 12*x^90 + 27*x^89 + 108*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 4*x^82 + 115*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 69*x^73 + 36*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 44*x^66 + 117*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 7*x^25 + 92*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 84*x^18 + 95*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 33*x^9 + 20*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 124*x^2 + 113*x + 60, x^93 + 74*x^91 + 96*x^90 + 99*x^89 + 96*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 38*x^83 + 32*x^82 + 43*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 29*x^73 + 32*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 50*x^67 + 96*x^66 + 29*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 111*x^25 + 96*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 94*x^19 + 32*x^18 + 119*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 25*x^9 + 32*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 42*x^3 + 96*x^2 + 121*x + 96, x^93 + 74*x^91 + 32*x^90 + 35*x^89 + 96*x^88 + 68*x^87 + x^85 + 102*x^83 + 32*x^82 + 43*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 93*x^73 + 32*x^72 + 116*x^71 + 7*x^69 + 114*x^67 + 96*x^66 + 29*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 47*x^25 + 96*x^24 + 116*x^23 + 37*x^21 + 30*x^19 + 32*x^18 + 119*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 89*x^9 + 32*x^8 + 68*x^7 + 27*x^5 + 106*x^3 + 96*x^2 + 121*x + 32, x^93 + 74*x^91 + 64*x^90 + 115*x^89 + 16*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 38*x^83 + 91*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 77*x^73 + 48*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 50*x^67 + 45*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 63*x^25 + 80*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 94*x^19 + 103*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 9*x^9 + 112*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 42*x^3 + 73*x + 16, x^93 + 74*x^91 + 4*x^90 + 59*x^89 + 36*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 108*x^82 + 19*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 37*x^73 + 12*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 36*x^66 + 85*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 39*x^25 + 116*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 92*x^18 + 127*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + x^9 + 92*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 20*x^2 + 81*x + 84, x^93 + 74*x^91 + 88*x^90 + 67*x^89 + 120*x^88 + 4*x^87 + 80*x^86 + x^85 + 80*x^84 + 38*x^83 + 8*x^82 + 75*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 61*x^73 + 40*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 88*x^66 + 125*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 79*x^25 + 88*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 40*x^18 + 23*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 57*x^9 + 8*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 120*x^2 + 89*x + 88, x^93 + 74*x^91 + 32*x^90 + 67*x^89 + 68*x^87 + 65*x^85 + 64*x^84 + 102*x^83 + 32*x^82 + 11*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 61*x^73 + 116*x^71 + 71*x^69 + 64*x^68 + 114*x^67 + 96*x^66 + 61*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 79*x^25 + 116*x^23 + 101*x^21 + 64*x^20 + 30*x^19 + 32*x^18 + 87*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 57*x^9 + 68*x^7 + 91*x^5 + 64*x^4 + 106*x^3 + 96*x^2 + 25*x + 64, x^93 + 74*x^91 + 88*x^90 + 115*x^89 + 72*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 8*x^82 + 27*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 77*x^73 + 24*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 88*x^66 + 109*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 63*x^25 + 104*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 40*x^18 + 39*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 9*x^9 + 56*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 120*x^2 + 9*x + 104, x^93 + 74*x^91 + 92*x^90 + 123*x^89 + 60*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 116*x^82 + 19*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 101*x^73 + 20*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 124*x^66 + 85*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 103*x^25 + 108*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 4*x^18 + 127*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 65*x^9 + 68*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 12*x^2 + 81*x + 76, x^93 + 74*x^91 + 64*x^90 + 35*x^89 + 96*x^88 + 4*x^87 + 65*x^85 + 64*x^84 + 38*x^83 + 64*x^82 + 107*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 93*x^73 + 32*x^72 + 52*x^71 + 71*x^69 + 64*x^68 + 50*x^67 + 64*x^66 + 93*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 47*x^25 + 96*x^24 + 52*x^23 + 101*x^21 + 64*x^20 + 94*x^19 + 64*x^18 + 55*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 89*x^9 + 32*x^8 + 4*x^7 + 91*x^5 + 64*x^4 + 42*x^3 + 64*x^2 + 57*x + 96, x^93 + 74*x^91 + 100*x^90 + 59*x^89 + 4*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 76*x^82 + 83*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 37*x^73 + 44*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 68*x^66 + 21*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 39*x^25 + 84*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 60*x^18 + 63*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + x^9 + 124*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 52*x^2 + 17*x + 116, x^93 + 74*x^91 + 52*x^90 + 75*x^89 + 36*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 124*x^82 + 3*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 85*x^73 + 12*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 84*x^66 + 37*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 119*x^25 + 116*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 44*x^18 + 47*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 113*x^9 + 92*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 4*x^2 + 97*x + 84, x^93 + 74*x^91 + 32*x^90 + 115*x^89 + 80*x^88 + 4*x^87 + 33*x^85 + 32*x^84 + 38*x^83 + 32*x^82 + 91*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 77*x^73 + 112*x^72 + 52*x^71 + 39*x^69 + 32*x^68 + 50*x^67 + 96*x^66 + 45*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 63*x^25 + 16*x^24 + 52*x^23 + 69*x^21 + 32*x^20 + 94*x^19 + 32*x^18 + 103*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 9*x^9 + 48*x^8 + 4*x^7 + 59*x^5 + 32*x^4 + 42*x^3 + 96*x^2 + 73*x + 80, x^93 + 74*x^91 + 72*x^90 + 83*x^89 + 120*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 102*x^83 + 88*x^82 + 59*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 109*x^73 + 40*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 114*x^67 + 72*x^66 + 77*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 31*x^25 + 88*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 30*x^19 + 56*x^18 + 71*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 41*x^9 + 8*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 106*x^3 + 40*x^2 + 105*x + 88, x^93 + 74*x^91 + 56*x^90 + 19*x^89 + 72*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 40*x^82 + 123*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 45*x^73 + 24*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 56*x^66 + 13*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 95*x^25 + 104*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 72*x^18 + 7*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 105*x^9 + 56*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 88*x^2 + 41*x + 104, x^93 + 74*x^91 + 100*x^90 + 59*x^89 + 68*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 12*x^82 + 19*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 37*x^73 + 108*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 4*x^66 + 85*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 39*x^25 + 20*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 124*x^18 + 127*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + x^9 + 60*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 116*x^2 + 81*x + 116, x^93 + 74*x^91 + 72*x^90 + 19*x^89 + 120*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 24*x^82 + 59*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 45*x^73 + 40*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 8*x^66 + 77*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 95*x^25 + 88*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 120*x^18 + 71*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 105*x^9 + 8*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 104*x^2 + 105*x + 24, x^93 + 74*x^91 + 92*x^90 + 43*x^89 + 108*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 116*x^82 + 99*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 117*x^73 + 36*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 124*x^66 + 69*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 87*x^25 + 92*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 4*x^18 + 15*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 17*x^9 + 20*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 12*x^2 + x + 60, x^93 + 74*x^91 + 80*x^90 + 83*x^89 + 64*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 102*x^83 + 112*x^82 + 59*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 109*x^73 + 64*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 114*x^67 + 80*x^66 + 77*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 31*x^25 + 64*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 30*x^19 + 48*x^18 + 71*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 41*x^9 + 64*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 106*x^3 + 16*x^2 + 105*x + 64, x^93 + 74*x^91 + 72*x^90 + 3*x^89 + 40*x^88 + 4*x^87 + 112*x^86 + x^85 + 112*x^84 + 38*x^83 + 88*x^82 + 11*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 125*x^73 + 56*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 72*x^66 + 61*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 15*x^25 + 72*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 56*x^18 + 87*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 121*x^9 + 88*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 40*x^2 + 25*x + 72, x^93 + 74*x^91 + 68*x^90 + 43*x^89 + 84*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 44*x^82 + 35*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 117*x^73 + 28*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 100*x^66 + 5*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 87*x^25 + 100*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 28*x^18 + 79*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 17*x^9 + 44*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 84*x^2 + 65*x + 68, x^93 + 74*x^91 + 8*x^90 + 51*x^89 + 88*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 24*x^82 + 91*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 13*x^73 + 72*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 8*x^66 + 45*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 127*x^25 + 56*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 120*x^18 + 103*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 73*x^9 + 40*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 104*x^2 + 73*x + 56, x^93 + 74*x^91 + 20*x^90 + 91*x^89 + 52*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 92*x^82 + 51*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 5*x^73 + 60*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 116*x^66 + 53*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 71*x^25 + 68*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 12*x^18 + 31*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 97*x^9 + 76*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 36*x^2 + 49*x + 100, x^93 + 74*x^91 + 92*x^90 + 91*x^89 + 60*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 116*x^82 + 51*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 5*x^73 + 20*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 124*x^66 + 53*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 71*x^25 + 108*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 4*x^18 + 31*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 97*x^9 + 68*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 12*x^2 + 49*x + 76, x^93 + 74*x^91 + 124*x^90 + 91*x^89 + 92*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 84*x^82 + 51*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 5*x^73 + 116*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 28*x^66 + 53*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 71*x^25 + 12*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 100*x^18 + 31*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 97*x^9 + 36*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 44*x^2 + 49*x + 108, x^93 + 74*x^91 + 112*x^90 + 35*x^89 + 48*x^88 + 68*x^87 + 96*x^86 + x^85 + 96*x^84 + 102*x^83 + 16*x^82 + 43*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 93*x^73 + 16*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 48*x^66 + 29*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 47*x^25 + 112*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 80*x^18 + 119*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 89*x^9 + 80*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 112*x^2 + 121*x + 48, x^93 + 74*x^91 + 20*x^90 + 123*x^89 + 20*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 92*x^82 + 19*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 101*x^73 + 92*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 116*x^66 + 85*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 103*x^25 + 36*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 12*x^18 + 127*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 65*x^9 + 108*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 36*x^2 + 81*x + 68, x^93 + 74*x^91 + 120*x^90 + 83*x^89 + 40*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 40*x^82 + 123*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 109*x^73 + 56*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 56*x^66 + 13*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 31*x^25 + 72*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 72*x^18 + 7*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 41*x^9 + 88*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 88*x^2 + 41*x + 8, x^93 + 74*x^91 + 64*x^90 + 83*x^89 + 112*x^88 + 68*x^87 + 33*x^85 + 32*x^84 + 102*x^83 + 64*x^82 + 59*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 109*x^73 + 80*x^72 + 116*x^71 + 39*x^69 + 32*x^68 + 114*x^67 + 64*x^66 + 77*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 31*x^25 + 48*x^24 + 116*x^23 + 69*x^21 + 32*x^20 + 30*x^19 + 64*x^18 + 71*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 41*x^9 + 16*x^8 + 68*x^7 + 59*x^5 + 32*x^4 + 106*x^3 + 64*x^2 + 105*x + 48, x^93 + 74*x^91 + 16*x^90 + 51*x^89 + 68*x^87 + 96*x^86 + 97*x^85 + 102*x^83 + 48*x^82 + 91*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 13*x^73 + 116*x^71 + 96*x^70 + 103*x^69 + 114*x^67 + 16*x^66 + 45*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 127*x^25 + 116*x^23 + 96*x^22 + 5*x^21 + 30*x^19 + 112*x^18 + 103*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 73*x^9 + 68*x^7 + 96*x^6 + 123*x^5 + 106*x^3 + 80*x^2 + 73*x, x^93 + 74*x^91 + 76*x^90 + 59*x^89 + 108*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 4*x^82 + 19*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 37*x^73 + 36*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 44*x^66 + 85*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 39*x^25 + 92*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 84*x^18 + 127*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + x^9 + 20*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 124*x^2 + 81*x + 124, x^93 + 74*x^91 + 16*x^90 + 3*x^89 + 80*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 112*x^82 + 75*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 125*x^73 + 112*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 80*x^66 + 125*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 15*x^25 + 16*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 48*x^18 + 23*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 121*x^9 + 48*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 16*x^2 + 89*x + 80, x^93 + 74*x^91 + 40*x^90 + 35*x^89 + 72*x^88 + 68*x^87 + 112*x^86 + x^85 + 112*x^84 + 102*x^83 + 56*x^82 + 43*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 93*x^73 + 24*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 104*x^66 + 29*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 47*x^25 + 104*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 24*x^18 + 119*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 89*x^9 + 56*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 72*x^2 + 121*x + 40, x^93 + 74*x^91 + 36*x^90 + 43*x^89 + 20*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 76*x^82 + 35*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 117*x^73 + 92*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 68*x^66 + 5*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 87*x^25 + 36*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 60*x^18 + 79*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 17*x^9 + 108*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 52*x^2 + 65*x + 4, x^93 + 74*x^91 + 80*x^90 + 35*x^89 + 80*x^88 + 68*x^87 + 32*x^86 + x^85 + 32*x^84 + 102*x^83 + 48*x^82 + 43*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 93*x^73 + 112*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 16*x^66 + 29*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 47*x^25 + 16*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 112*x^18 + 119*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 89*x^9 + 48*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 80*x^2 + 121*x + 80, x^93 + 74*x^91 + 80*x^90 + 83*x^89 + 32*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 112*x^82 + 59*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 109*x^73 + 96*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 80*x^66 + 77*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 31*x^25 + 32*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 48*x^18 + 71*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 41*x^9 + 96*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 16*x^2 + 105*x + 32, x^93 + 74*x^91 + 116*x^90 + 43*x^89 + 4*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 124*x^82 + 99*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 117*x^73 + 44*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 84*x^66 + 69*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 87*x^25 + 84*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 44*x^18 + 15*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 17*x^9 + 124*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 4*x^2 + x + 116, x^93 + 74*x^91 + 100*x^90 + 43*x^89 + 20*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 12*x^82 + 35*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 117*x^73 + 92*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 4*x^66 + 5*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 87*x^25 + 36*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 124*x^18 + 79*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 17*x^9 + 108*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 116*x^2 + 65*x + 4, x^93 + 74*x^91 + 19*x^89 + 16*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 38*x^83 + 64*x^82 + 59*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 45*x^73 + 48*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 50*x^67 + 64*x^66 + 77*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 95*x^25 + 80*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 94*x^19 + 64*x^18 + 71*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 105*x^9 + 112*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 42*x^3 + 64*x^2 + 105*x + 16, x^93 + 74*x^91 + 88*x^90 + 3*x^89 + 24*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 72*x^82 + 75*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 125*x^73 + 8*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 24*x^66 + 125*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 15*x^25 + 120*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 104*x^18 + 23*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 121*x^9 + 104*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 56*x^2 + 89*x + 56, x^93 + 74*x^91 + 28*x^90 + 59*x^89 + 124*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 116*x^82 + 19*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 37*x^73 + 84*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 124*x^66 + 85*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 39*x^25 + 44*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 4*x^18 + 127*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + x^9 + 4*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 12*x^2 + 81*x + 76, x^93 + 74*x^91 + 16*x^90 + 35*x^89 + 48*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 48*x^82 + 107*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 93*x^73 + 16*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 16*x^66 + 93*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 47*x^25 + 112*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 112*x^18 + 55*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 89*x^9 + 80*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 80*x^2 + 57*x + 112, x^93 + 74*x^91 + 92*x^90 + 11*x^89 + 44*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 116*x^82 + 3*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 21*x^73 + 100*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 124*x^66 + 37*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 55*x^25 + 28*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 4*x^18 + 47*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 49*x^9 + 84*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 12*x^2 + 97*x + 124, x^93 + 74*x^91 + 24*x^90 + 83*x^89 + 40*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 72*x^82 + 59*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 109*x^73 + 56*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 24*x^66 + 77*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 31*x^25 + 72*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 104*x^18 + 71*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 41*x^9 + 88*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 56*x^2 + 105*x + 72, x^93 + 74*x^91 + 124*x^90 + 43*x^89 + 108*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 84*x^82 + 99*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 117*x^73 + 36*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 28*x^66 + 69*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 87*x^25 + 92*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 100*x^18 + 15*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 17*x^9 + 20*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 44*x^2 + x + 60, x^93 + 74*x^91 + 68*x^90 + 107*x^89 + 84*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 44*x^82 + 99*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 53*x^73 + 28*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 100*x^66 + 69*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 23*x^25 + 100*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 28*x^18 + 15*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 81*x^9 + 44*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 84*x^2 + x + 68, x^93 + 74*x^91 + 116*x^90 + 123*x^89 + 20*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 60*x^82 + 83*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 101*x^73 + 92*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 20*x^66 + 21*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 103*x^25 + 36*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 108*x^18 + 63*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 65*x^9 + 108*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 68*x^2 + 17*x + 4, x^93 + 74*x^91 + 88*x^90 + 3*x^89 + 120*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 72*x^82 + 75*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 125*x^73 + 40*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 24*x^66 + 125*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 15*x^25 + 88*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 104*x^18 + 23*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 121*x^9 + 8*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 56*x^2 + 89*x + 24, x^93 + 74*x^91 + 36*x^90 + 75*x^89 + 116*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 76*x^82 + 3*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 85*x^73 + 124*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 68*x^66 + 37*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 119*x^25 + 4*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 60*x^18 + 47*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 113*x^9 + 12*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 52*x^2 + 97*x + 100, x^93 + 74*x^91 + 60*x^90 + 123*x^89 + 92*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 20*x^82 + 19*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 101*x^73 + 116*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 92*x^66 + 85*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 103*x^25 + 12*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 36*x^18 + 127*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 65*x^9 + 36*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 108*x^2 + 81*x + 108, x^93 + 74*x^91 + 24*x^90 + 67*x^89 + 120*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 8*x^82 + 11*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 61*x^73 + 40*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 88*x^66 + 61*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 79*x^25 + 88*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 40*x^18 + 87*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 57*x^9 + 8*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 120*x^2 + 25*x + 24, x^93 + 74*x^91 + 84*x^90 + 27*x^89 + 116*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 28*x^82 + 115*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 69*x^73 + 124*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 52*x^66 + 117*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 7*x^25 + 4*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 76*x^18 + 95*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 33*x^9 + 12*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 100*x^2 + 113*x + 36, x^93 + 74*x^91 + 36*x^90 + 123*x^89 + 100*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 76*x^82 + 83*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 101*x^73 + 76*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 68*x^66 + 21*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 103*x^25 + 52*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 60*x^18 + 63*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 65*x^9 + 28*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 52*x^2 + 17*x + 20, x^93 + 74*x^91 + 68*x^90 + 91*x^89 + 100*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 108*x^82 + 51*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 5*x^73 + 76*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 36*x^66 + 53*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 71*x^25 + 52*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 92*x^18 + 31*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 97*x^9 + 28*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 20*x^2 + 49*x + 84, x^93 + 74*x^91 + 120*x^90 + 83*x^89 + 104*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 40*x^82 + 123*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 109*x^73 + 120*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 56*x^66 + 13*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 31*x^25 + 8*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 72*x^18 + 7*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 41*x^9 + 24*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 88*x^2 + 41*x + 72, x^93 + 74*x^91 + 12*x^90 + 91*x^89 + 108*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 4*x^82 + 51*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 5*x^73 + 36*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 44*x^66 + 53*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 71*x^25 + 92*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 84*x^18 + 31*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 97*x^9 + 20*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 124*x^2 + 49*x + 60, x^93 + 74*x^91 + 124*x^90 + 107*x^89 + 76*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 84*x^82 + 35*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 53*x^73 + 68*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 28*x^66 + 5*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 23*x^25 + 60*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 100*x^18 + 79*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 81*x^9 + 52*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 44*x^2 + 65*x + 28, x^93 + 74*x^91 + 24*x^90 + 99*x^89 + 120*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 72*x^82 + 43*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 29*x^73 + 40*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 24*x^66 + 29*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 111*x^25 + 88*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 104*x^18 + 119*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 25*x^9 + 8*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 56*x^2 + 121*x + 88, x^93 + 74*x^91 + 44*x^90 + 123*x^89 + 76*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 36*x^82 + 83*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 101*x^73 + 68*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 12*x^66 + 21*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 103*x^25 + 60*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 116*x^18 + 63*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 65*x^9 + 52*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 92*x^2 + 17*x + 92, x^93 + 74*x^91 + 52*x^90 + 107*x^89 + 100*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 60*x^82 + 35*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 53*x^73 + 76*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 20*x^66 + 5*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 23*x^25 + 52*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 108*x^18 + 79*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 81*x^9 + 28*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 68*x^2 + 65*x + 84, x^93 + 74*x^91 + 28*x^90 + 59*x^89 + 124*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 52*x^82 + 83*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 37*x^73 + 84*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 60*x^66 + 21*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 39*x^25 + 44*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 68*x^18 + 63*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + x^9 + 4*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 76*x^2 + 17*x + 12, x^93 + 74*x^91 + 64*x^90 + 67*x^89 + 96*x^88 + 4*x^87 + x^85 + 64*x^84 + 38*x^83 + 64*x^82 + 75*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 61*x^73 + 32*x^72 + 52*x^71 + 7*x^69 + 64*x^68 + 50*x^67 + 64*x^66 + 125*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 79*x^25 + 96*x^24 + 52*x^23 + 37*x^21 + 64*x^20 + 94*x^19 + 64*x^18 + 23*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 57*x^9 + 32*x^8 + 4*x^7 + 27*x^5 + 64*x^4 + 42*x^3 + 64*x^2 + 89*x + 96, x^93 + 74*x^91 + 28*x^90 + 107*x^89 + 44*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 116*x^82 + 99*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 53*x^73 + 100*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 124*x^66 + 69*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 23*x^25 + 28*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 4*x^18 + 15*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 81*x^9 + 84*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 12*x^2 + x + 60, x^93 + 74*x^91 + 32*x^90 + 51*x^89 + 80*x^88 + 4*x^87 + 33*x^85 + 32*x^84 + 38*x^83 + 32*x^82 + 27*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 13*x^73 + 112*x^72 + 52*x^71 + 39*x^69 + 32*x^68 + 50*x^67 + 96*x^66 + 109*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 127*x^25 + 16*x^24 + 52*x^23 + 69*x^21 + 32*x^20 + 94*x^19 + 32*x^18 + 39*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 73*x^9 + 48*x^8 + 4*x^7 + 59*x^5 + 32*x^4 + 42*x^3 + 96*x^2 + 9*x + 80, x^93 + 74*x^91 + 108*x^90 + 11*x^89 + 60*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 36*x^82 + 3*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 21*x^73 + 20*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 12*x^66 + 37*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 55*x^25 + 108*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 116*x^18 + 47*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 49*x^9 + 68*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 92*x^2 + 97*x + 76, x^93 + 74*x^91 + 44*x^90 + 43*x^89 + 124*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 100*x^82 + 99*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 117*x^73 + 84*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 76*x^66 + 69*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 87*x^25 + 44*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 52*x^18 + 15*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 17*x^9 + 4*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 28*x^2 + x + 12, x^93 + 74*x^91 + 80*x^90 + 35*x^89 + 112*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 112*x^82 + 107*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 93*x^73 + 80*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 80*x^66 + 93*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 47*x^25 + 48*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 48*x^18 + 55*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 89*x^9 + 16*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 16*x^2 + 57*x + 48, x^93 + 74*x^91 + 108*x^90 + 59*x^89 + 12*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 36*x^82 + 83*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 37*x^73 + 4*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 12*x^66 + 21*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 39*x^25 + 124*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 116*x^18 + 63*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + x^9 + 116*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 92*x^2 + 17*x + 92, x^93 + 74*x^91 + 96*x^90 + 51*x^89 + 48*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 102*x^83 + 32*x^82 + 91*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 13*x^73 + 16*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 114*x^67 + 96*x^66 + 45*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 127*x^25 + 112*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 30*x^19 + 32*x^18 + 103*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 73*x^9 + 80*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 106*x^3 + 96*x^2 + 73*x + 112, x^93 + 74*x^91 + 56*x^90 + 83*x^89 + 8*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 104*x^82 + 123*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 109*x^73 + 88*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 120*x^66 + 13*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 31*x^25 + 40*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 8*x^18 + 7*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 41*x^9 + 120*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 24*x^2 + 41*x + 104, x^93 + 74*x^91 + 20*x^90 + 27*x^89 + 20*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 28*x^82 + 51*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 69*x^73 + 92*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 52*x^66 + 53*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 7*x^25 + 36*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 76*x^18 + 31*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 33*x^9 + 108*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 100*x^2 + 49*x + 4, x^93 + 74*x^91 + 20*x^90 + 107*x^89 + 100*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 92*x^82 + 35*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 53*x^73 + 76*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 116*x^66 + 5*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 23*x^25 + 52*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 12*x^18 + 79*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 81*x^9 + 28*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 36*x^2 + 65*x + 84, x^93 + 74*x^91 + 28*x^90 + 123*x^89 + 124*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 116*x^82 + 83*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 101*x^73 + 84*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 124*x^66 + 21*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 103*x^25 + 44*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 4*x^18 + 63*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 65*x^9 + 4*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 12*x^2 + 17*x + 76, x^93 + 74*x^91 + 104*x^90 + 51*x^89 + 88*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 56*x^82 + 91*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 13*x^73 + 72*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 104*x^66 + 45*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 127*x^25 + 56*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 24*x^18 + 103*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 73*x^9 + 40*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 72*x^2 + 73*x + 56, x^93 + 74*x^91 + 4*x^90 + 11*x^89 + 20*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 44*x^82 + 3*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 21*x^73 + 92*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 100*x^66 + 37*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 55*x^25 + 36*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 28*x^18 + 47*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 49*x^9 + 108*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 84*x^2 + 97*x + 68, x^93 + 74*x^91 + 96*x^90 + 3*x^89 + 64*x^88 + 68*x^87 + 65*x^85 + 64*x^84 + 102*x^83 + 96*x^82 + 75*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 125*x^73 + 64*x^72 + 116*x^71 + 71*x^69 + 64*x^68 + 114*x^67 + 32*x^66 + 125*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 15*x^25 + 64*x^24 + 116*x^23 + 101*x^21 + 64*x^20 + 30*x^19 + 96*x^18 + 23*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 121*x^9 + 64*x^8 + 68*x^7 + 91*x^5 + 64*x^4 + 106*x^3 + 32*x^2 + 89*x, x^93 + 74*x^91 + 28*x^90 + 27*x^89 + 92*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 52*x^82 + 115*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 69*x^73 + 116*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 60*x^66 + 117*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 7*x^25 + 12*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 68*x^18 + 95*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 33*x^9 + 36*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 76*x^2 + 113*x + 108, x^93 + 74*x^91 + 56*x^90 + 115*x^89 + 8*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 104*x^82 + 91*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 77*x^73 + 88*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 120*x^66 + 45*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 63*x^25 + 40*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 8*x^18 + 103*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 9*x^9 + 120*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 24*x^2 + 73*x + 104, x^93 + 74*x^91 + 120*x^90 + 35*x^89 + 24*x^88 + 68*x^87 + 80*x^86 + x^85 + 80*x^84 + 102*x^83 + 40*x^82 + 43*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 93*x^73 + 8*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 56*x^66 + 29*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 47*x^25 + 120*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 72*x^18 + 119*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 89*x^9 + 104*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 88*x^2 + 121*x + 56, x^93 + 74*x^91 + 51*x^89 + 112*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 38*x^83 + 64*x^82 + 27*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 13*x^73 + 80*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 50*x^67 + 64*x^66 + 109*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 127*x^25 + 48*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 94*x^19 + 64*x^18 + 39*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 73*x^9 + 16*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 42*x^3 + 64*x^2 + 9*x + 112, x^93 + 74*x^91 + 35*x^89 + 32*x^88 + 68*x^87 + 64*x^86 + x^85 + 102*x^83 + 64*x^82 + 43*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 93*x^73 + 96*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 114*x^67 + 64*x^66 + 29*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 47*x^25 + 32*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 30*x^19 + 64*x^18 + 119*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 89*x^9 + 96*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 106*x^3 + 64*x^2 + 121*x + 96, x^93 + 74*x^91 + 28*x^90 + 107*x^89 + 108*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 52*x^82 + 35*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 53*x^73 + 36*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 60*x^66 + 5*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 23*x^25 + 92*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 68*x^18 + 79*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 81*x^9 + 20*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 76*x^2 + 65*x + 60, x^93 + 74*x^91 + 60*x^90 + 107*x^89 + 12*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 20*x^82 + 35*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 53*x^73 + 4*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 92*x^66 + 5*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 23*x^25 + 124*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 36*x^18 + 79*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 81*x^9 + 116*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 108*x^2 + 65*x + 92, x^93 + 74*x^91 + 28*x^90 + 43*x^89 + 76*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 52*x^82 + 99*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 117*x^73 + 68*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 60*x^66 + 69*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 87*x^25 + 60*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 68*x^18 + 15*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 17*x^9 + 52*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 76*x^2 + x + 28, x^93 + 74*x^91 + 4*x^90 + 107*x^89 + 20*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 44*x^82 + 35*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 53*x^73 + 92*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 100*x^66 + 5*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 23*x^25 + 36*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 28*x^18 + 79*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 81*x^9 + 108*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 84*x^2 + 65*x + 68, x^93 + 74*x^91 + 80*x^90 + 115*x^89 + 32*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 38*x^83 + 48*x^82 + 91*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 77*x^73 + 96*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 50*x^67 + 16*x^66 + 45*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 63*x^25 + 32*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 94*x^19 + 112*x^18 + 103*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 9*x^9 + 96*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 42*x^3 + 80*x^2 + 73*x + 96, x^93 + 74*x^91 + 100*x^90 + 91*x^89 + 36*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 76*x^82 + 51*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 5*x^73 + 12*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 68*x^66 + 53*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 71*x^25 + 116*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 60*x^18 + 31*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 97*x^9 + 92*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 52*x^2 + 49*x + 20, x^93 + 74*x^91 + 24*x^90 + 67*x^89 + 24*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 8*x^82 + 11*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 61*x^73 + 8*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 88*x^66 + 61*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 79*x^25 + 120*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 40*x^18 + 87*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 57*x^9 + 104*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 120*x^2 + 25*x + 56, x^93 + 74*x^91 + 48*x^90 + 19*x^89 + 96*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 16*x^82 + 123*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 45*x^73 + 32*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 48*x^66 + 13*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 95*x^25 + 96*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 80*x^18 + 7*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 105*x^9 + 32*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 112*x^2 + 41*x + 96, x^93 + 74*x^91 + 108*x^90 + 91*x^89 + 12*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 36*x^82 + 51*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 5*x^73 + 4*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 12*x^66 + 53*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 71*x^25 + 124*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 116*x^18 + 31*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 97*x^9 + 116*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 92*x^2 + 49*x + 92, x^93 + 74*x^91 + 36*x^90 + 27*x^89 + 4*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 76*x^82 + 51*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 69*x^73 + 44*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 68*x^66 + 53*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 7*x^25 + 84*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 60*x^18 + 31*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 33*x^9 + 124*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 52*x^2 + 49*x + 52, x^93 + 74*x^91 + 72*x^90 + 83*x^89 + 120*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 24*x^82 + 123*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 109*x^73 + 40*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 8*x^66 + 13*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 31*x^25 + 88*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 120*x^18 + 7*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 41*x^9 + 8*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 104*x^2 + 41*x + 24, x^93 + 74*x^91 + 96*x^90 + 83*x^89 + 80*x^88 + 4*x^87 + 97*x^85 + 32*x^84 + 38*x^83 + 96*x^82 + 123*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 109*x^73 + 112*x^72 + 52*x^71 + 103*x^69 + 32*x^68 + 50*x^67 + 32*x^66 + 13*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 31*x^25 + 16*x^24 + 52*x^23 + 5*x^21 + 32*x^20 + 94*x^19 + 96*x^18 + 7*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 41*x^9 + 48*x^8 + 4*x^7 + 123*x^5 + 32*x^4 + 42*x^3 + 32*x^2 + 41*x + 80, x^93 + 74*x^91 + 120*x^90 + 83*x^89 + 72*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 104*x^82 + 59*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 109*x^73 + 24*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 120*x^66 + 77*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 31*x^25 + 104*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 8*x^18 + 71*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 41*x^9 + 56*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 24*x^2 + 105*x + 104, x^93 + 74*x^91 + 80*x^90 + 67*x^89 + 48*x^88 + 4*x^87 + 96*x^86 + x^85 + 32*x^84 + 38*x^83 + 112*x^82 + 75*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 61*x^73 + 16*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 80*x^66 + 125*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 79*x^25 + 112*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 48*x^18 + 23*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 57*x^9 + 80*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 16*x^2 + 89*x + 112, x^93 + 74*x^91 + 76*x^90 + 27*x^89 + 76*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 4*x^82 + 51*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 69*x^73 + 68*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 44*x^66 + 53*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 7*x^25 + 60*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 84*x^18 + 31*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 33*x^9 + 52*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 124*x^2 + 49*x + 92, x^93 + 74*x^91 + 32*x^90 + 51*x^89 + 112*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 102*x^83 + 96*x^82 + 91*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 13*x^73 + 80*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 114*x^67 + 32*x^66 + 45*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 127*x^25 + 48*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 30*x^19 + 96*x^18 + 103*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 73*x^9 + 16*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 106*x^3 + 32*x^2 + 73*x + 48, x^93 + 74*x^91 + 56*x^90 + 115*x^89 + 104*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 104*x^82 + 91*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 77*x^73 + 120*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 120*x^66 + 45*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 63*x^25 + 8*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 8*x^18 + 103*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 9*x^9 + 24*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 24*x^2 + 73*x + 72, x^93 + 74*x^91 + 124*x^90 + 43*x^89 + 12*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 84*x^82 + 99*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 117*x^73 + 4*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 28*x^66 + 69*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 87*x^25 + 124*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 100*x^18 + 15*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 17*x^9 + 116*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 44*x^2 + x + 92, x^93 + 74*x^91 + 4*x^90 + 11*x^89 + 116*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 44*x^82 + 3*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 21*x^73 + 124*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 100*x^66 + 37*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 55*x^25 + 4*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 28*x^18 + 47*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 49*x^9 + 12*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 84*x^2 + 97*x + 36, x^93 + 74*x^91 + 64*x^90 + 67*x^89 + 32*x^88 + 4*x^87 + x^85 + 64*x^84 + 38*x^83 + 64*x^82 + 75*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 61*x^73 + 96*x^72 + 52*x^71 + 7*x^69 + 64*x^68 + 50*x^67 + 64*x^66 + 125*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 79*x^25 + 32*x^24 + 52*x^23 + 37*x^21 + 64*x^20 + 94*x^19 + 64*x^18 + 23*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 57*x^9 + 96*x^8 + 4*x^7 + 27*x^5 + 64*x^4 + 42*x^3 + 64*x^2 + 89*x + 32, x^93 + 74*x^91 + 96*x^90 + 35*x^89 + 64*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 38*x^83 + 32*x^82 + 107*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 93*x^73 + 64*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 50*x^67 + 96*x^66 + 93*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 47*x^25 + 64*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 94*x^19 + 32*x^18 + 55*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 89*x^9 + 64*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 42*x^3 + 96*x^2 + 57*x + 64, x^93 + 74*x^91 + 36*x^90 + 11*x^89 + 116*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 12*x^82 + 3*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 21*x^73 + 124*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 4*x^66 + 37*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 55*x^25 + 4*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 124*x^18 + 47*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 49*x^9 + 12*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 116*x^2 + 97*x + 36, x^93 + 74*x^91 + 48*x^90 + 115*x^89 + 68*x^87 + 32*x^86 + 97*x^85 + 102*x^83 + 16*x^82 + 27*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 77*x^73 + 116*x^71 + 32*x^70 + 103*x^69 + 114*x^67 + 48*x^66 + 109*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 63*x^25 + 116*x^23 + 32*x^22 + 5*x^21 + 30*x^19 + 80*x^18 + 39*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 9*x^9 + 68*x^7 + 32*x^6 + 123*x^5 + 106*x^3 + 112*x^2 + 9*x, x^93 + 74*x^91 + 32*x^90 + 67*x^89 + 4*x^87 + 64*x^86 + x^85 + 38*x^83 + 96*x^82 + 75*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 61*x^73 + 52*x^71 + 64*x^70 + 7*x^69 + 50*x^67 + 32*x^66 + 125*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 79*x^25 + 52*x^23 + 64*x^22 + 37*x^21 + 94*x^19 + 96*x^18 + 23*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 57*x^9 + 4*x^7 + 64*x^6 + 27*x^5 + 42*x^3 + 32*x^2 + 89*x, x^93 + 74*x^91 + 16*x^90 + 3*x^89 + 16*x^88 + 4*x^87 + 96*x^86 + x^85 + 96*x^84 + 38*x^83 + 48*x^82 + 11*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 125*x^73 + 48*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 16*x^66 + 61*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 15*x^25 + 80*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 112*x^18 + 87*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 121*x^9 + 112*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 80*x^2 + 25*x + 80, x^93 + 74*x^91 + 99*x^89 + 64*x^88 + 4*x^87 + 65*x^85 + 38*x^83 + 43*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 29*x^73 + 64*x^72 + 52*x^71 + 71*x^69 + 50*x^67 + 29*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 111*x^25 + 64*x^24 + 52*x^23 + 101*x^21 + 94*x^19 + 119*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 25*x^9 + 64*x^8 + 4*x^7 + 91*x^5 + 42*x^3 + 121*x + 64, x^93 + 74*x^91 + 56*x^90 + 115*x^89 + 72*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 40*x^82 + 27*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 77*x^73 + 24*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 56*x^66 + 109*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 63*x^25 + 104*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 72*x^18 + 39*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 9*x^9 + 56*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 88*x^2 + 9*x + 104, x^93 + 74*x^91 + 8*x^90 + 115*x^89 + 24*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 88*x^82 + 91*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 77*x^73 + 8*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 72*x^66 + 45*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 63*x^25 + 120*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 56*x^18 + 103*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 9*x^9 + 104*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 40*x^2 + 73*x + 56, x^93 + 74*x^91 + 51*x^89 + 48*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 38*x^83 + 64*x^82 + 27*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 13*x^73 + 16*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 50*x^67 + 64*x^66 + 109*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 127*x^25 + 112*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 94*x^19 + 64*x^18 + 39*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 73*x^9 + 80*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 42*x^3 + 64*x^2 + 9*x + 48, x^93 + 74*x^91 + 120*x^90 + 19*x^89 + 40*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 104*x^82 + 123*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 45*x^73 + 56*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 120*x^66 + 13*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 95*x^25 + 72*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 8*x^18 + 7*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 105*x^9 + 88*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 24*x^2 + 41*x + 72, x^93 + 74*x^91 + 32*x^90 + 67*x^89 + 32*x^88 + 68*x^87 + 65*x^85 + 102*x^83 + 32*x^82 + 11*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 61*x^73 + 96*x^72 + 116*x^71 + 71*x^69 + 114*x^67 + 96*x^66 + 61*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 79*x^25 + 32*x^24 + 116*x^23 + 101*x^21 + 30*x^19 + 32*x^18 + 87*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 57*x^9 + 96*x^8 + 68*x^7 + 91*x^5 + 106*x^3 + 96*x^2 + 25*x + 96, x^93 + 74*x^91 + 84*x^90 + 59*x^89 + 84*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 92*x^82 + 19*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 37*x^73 + 28*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 116*x^66 + 85*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 39*x^25 + 100*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 12*x^18 + 127*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + x^9 + 44*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 36*x^2 + 81*x + 68, x^93 + 74*x^91 + 92*x^90 + 43*x^89 + 76*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 52*x^82 + 35*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 117*x^73 + 68*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 60*x^66 + 5*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 87*x^25 + 60*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 68*x^18 + 79*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 17*x^9 + 52*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 76*x^2 + 65*x + 92, x^93 + 74*x^91 + 96*x^90 + 67*x^89 + 96*x^88 + 4*x^87 + 64*x^86 + x^85 + 64*x^84 + 38*x^83 + 32*x^82 + 75*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 61*x^73 + 32*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 50*x^67 + 96*x^66 + 125*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 79*x^25 + 96*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 94*x^19 + 32*x^18 + 23*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 57*x^9 + 32*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 42*x^3 + 96*x^2 + 89*x + 96, x^93 + 74*x^91 + 120*x^90 + 35*x^89 + 56*x^88 + 68*x^87 + 80*x^86 + x^85 + 16*x^84 + 102*x^83 + 40*x^82 + 43*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 93*x^73 + 104*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 56*x^66 + 29*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 47*x^25 + 24*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 72*x^18 + 119*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 89*x^9 + 72*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 88*x^2 + 121*x + 88, x^93 + 74*x^91 + 4*x^90 + 11*x^89 + 84*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 108*x^82 + 67*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 21*x^73 + 28*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 36*x^66 + 101*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 55*x^25 + 100*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 92*x^18 + 111*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 49*x^9 + 44*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 20*x^2 + 33*x + 68, x^93 + 74*x^91 + 40*x^90 + 51*x^89 + 56*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 120*x^82 + 91*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 13*x^73 + 104*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 40*x^66 + 45*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 127*x^25 + 24*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 88*x^18 + 103*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 73*x^9 + 72*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 8*x^2 + 73*x + 24, x^93 + 74*x^91 + 4*x^90 + 27*x^89 + 68*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 108*x^82 + 51*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 69*x^73 + 108*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 36*x^66 + 53*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 7*x^25 + 20*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 92*x^18 + 31*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 33*x^9 + 60*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 20*x^2 + 49*x + 116, x^93 + 74*x^91 + 8*x^90 + 67*x^89 + 104*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 88*x^82 + 11*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 61*x^73 + 120*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 72*x^66 + 61*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 79*x^25 + 8*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 56*x^18 + 87*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 57*x^9 + 24*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 40*x^2 + 25*x + 72, x^93 + 74*x^91 + 60*x^90 + 123*x^89 + 124*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 84*x^82 + 83*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 101*x^73 + 84*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 28*x^66 + 21*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 103*x^25 + 44*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 100*x^18 + 63*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 65*x^9 + 4*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 44*x^2 + 17*x + 76, x^93 + 74*x^91 + 32*x^90 + 19*x^89 + 16*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 102*x^83 + 96*x^82 + 123*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 45*x^73 + 48*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 114*x^67 + 32*x^66 + 13*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 95*x^25 + 80*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 30*x^19 + 96*x^18 + 7*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 105*x^9 + 112*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 106*x^3 + 32*x^2 + 41*x + 80, x^93 + 74*x^91 + 28*x^90 + 11*x^89 + 108*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 52*x^82 + 3*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 21*x^73 + 36*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 60*x^66 + 37*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 55*x^25 + 92*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 68*x^18 + 47*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 49*x^9 + 20*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 76*x^2 + 97*x + 60, x^93 + 74*x^91 + 52*x^90 + 11*x^89 + 100*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 60*x^82 + 3*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 21*x^73 + 76*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 20*x^66 + 37*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 55*x^25 + 52*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 108*x^18 + 47*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 49*x^9 + 28*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 68*x^2 + 97*x + 84, x^93 + 74*x^91 + 96*x^90 + 83*x^89 + 16*x^88 + 4*x^87 + 97*x^85 + 32*x^84 + 38*x^83 + 96*x^82 + 123*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 109*x^73 + 48*x^72 + 52*x^71 + 103*x^69 + 32*x^68 + 50*x^67 + 32*x^66 + 13*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 31*x^25 + 80*x^24 + 52*x^23 + 5*x^21 + 32*x^20 + 94*x^19 + 96*x^18 + 7*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 41*x^9 + 112*x^8 + 4*x^7 + 123*x^5 + 32*x^4 + 42*x^3 + 32*x^2 + 41*x + 16, x^93 + 74*x^91 + 44*x^90 + 75*x^89 + 124*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 36*x^82 + 3*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 85*x^73 + 84*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 12*x^66 + 37*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 119*x^25 + 44*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 116*x^18 + 47*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 113*x^9 + 4*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 92*x^2 + 97*x + 76, x^93 + 74*x^91 + 92*x^90 + 123*x^89 + 92*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 52*x^82 + 83*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 101*x^73 + 116*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 60*x^66 + 21*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 103*x^25 + 12*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 68*x^18 + 63*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 65*x^9 + 36*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 76*x^2 + 17*x + 44, x^93 + 74*x^91 + 80*x^90 + 67*x^89 + 112*x^88 + 4*x^87 + 96*x^86 + x^85 + 32*x^84 + 38*x^83 + 112*x^82 + 75*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 61*x^73 + 80*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 80*x^66 + 125*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 79*x^25 + 48*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 48*x^18 + 23*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 57*x^9 + 16*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 16*x^2 + 89*x + 48, x^93 + 74*x^91 + 124*x^90 + 75*x^89 + 108*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 84*x^82 + 67*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 85*x^73 + 36*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 28*x^66 + 101*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 119*x^25 + 92*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 100*x^18 + 111*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 113*x^9 + 20*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 44*x^2 + 33*x + 60, x^93 + 74*x^91 + 116*x^90 + 27*x^89 + 20*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 124*x^82 + 115*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 69*x^73 + 92*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 84*x^66 + 117*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 7*x^25 + 36*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 44*x^18 + 95*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 33*x^9 + 108*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 4*x^2 + 113*x + 68, x^93 + 74*x^91 + 56*x^90 + 19*x^89 + 8*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 40*x^82 + 123*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 45*x^73 + 88*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 56*x^66 + 13*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 95*x^25 + 40*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 72*x^18 + 7*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 105*x^9 + 120*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 88*x^2 + 41*x + 40, x^93 + 74*x^91 + 32*x^90 + 99*x^89 + 96*x^88 + 68*x^87 + x^85 + 102*x^83 + 32*x^82 + 107*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 29*x^73 + 32*x^72 + 116*x^71 + 7*x^69 + 114*x^67 + 96*x^66 + 93*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 111*x^25 + 96*x^24 + 116*x^23 + 37*x^21 + 30*x^19 + 32*x^18 + 55*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 25*x^9 + 32*x^8 + 68*x^7 + 27*x^5 + 106*x^3 + 96*x^2 + 57*x + 32, x^93 + 74*x^91 + 20*x^90 + 59*x^89 + 20*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 28*x^82 + 19*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 37*x^73 + 92*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 52*x^66 + 85*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 39*x^25 + 36*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 76*x^18 + 127*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + x^9 + 108*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 100*x^2 + 81*x + 4, x^93 + 74*x^91 + 116*x^90 + 123*x^89 + 116*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 60*x^82 + 83*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 101*x^73 + 124*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 20*x^66 + 21*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 103*x^25 + 4*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 108*x^18 + 63*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 65*x^9 + 12*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 68*x^2 + 17*x + 100, x^93 + 74*x^91 + 92*x^90 + 91*x^89 + 28*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 116*x^82 + 51*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 5*x^73 + 52*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 124*x^66 + 53*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 71*x^25 + 76*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 4*x^18 + 31*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 97*x^9 + 100*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 12*x^2 + 49*x + 44, x^93 + 74*x^91 + 72*x^90 + 99*x^89 + 8*x^88 + 68*x^87 + 48*x^86 + x^85 + 112*x^84 + 102*x^83 + 24*x^82 + 107*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 29*x^73 + 88*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 8*x^66 + 93*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 111*x^25 + 40*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 120*x^18 + 55*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 25*x^9 + 120*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 104*x^2 + 57*x + 104, x^93 + 74*x^91 + 72*x^90 + 19*x^89 + 56*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 24*x^82 + 59*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 45*x^73 + 104*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 8*x^66 + 77*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 95*x^25 + 24*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 120*x^18 + 71*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 105*x^9 + 72*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 104*x^2 + 105*x + 88, x^93 + 74*x^91 + 104*x^90 + 3*x^89 + 40*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 120*x^82 + 75*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 125*x^73 + 56*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 40*x^66 + 125*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 15*x^25 + 72*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 88*x^18 + 23*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 121*x^9 + 88*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 8*x^2 + 89*x + 8, x^93 + 74*x^91 + 88*x^90 + 3*x^89 + 24*x^88 + 4*x^87 + 80*x^86 + x^85 + 16*x^84 + 38*x^83 + 8*x^82 + 11*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 125*x^73 + 8*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 88*x^66 + 61*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 15*x^25 + 120*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 40*x^18 + 87*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 121*x^9 + 104*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 120*x^2 + 25*x + 120, x^93 + 74*x^91 + 72*x^90 + 3*x^89 + 104*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 24*x^82 + 75*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 125*x^73 + 120*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 8*x^66 + 125*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 15*x^25 + 8*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 120*x^18 + 23*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 121*x^9 + 24*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 104*x^2 + 89*x + 72, x^93 + 74*x^91 + 44*x^90 + 11*x^89 + 124*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 100*x^82 + 3*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 21*x^73 + 84*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 76*x^66 + 37*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 55*x^25 + 44*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 52*x^18 + 47*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 49*x^9 + 4*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 28*x^2 + 97*x + 12, x^93 + 74*x^91 + 72*x^90 + 19*x^89 + 88*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 88*x^82 + 123*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 45*x^73 + 72*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 72*x^66 + 13*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 95*x^25 + 56*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 56*x^18 + 7*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 105*x^9 + 40*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 40*x^2 + 41*x + 56, x^93 + 74*x^91 + 88*x^90 + 51*x^89 + 104*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 8*x^82 + 91*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 13*x^73 + 120*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 88*x^66 + 45*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 127*x^25 + 8*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 40*x^18 + 103*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 73*x^9 + 24*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 120*x^2 + 73*x + 8, x^93 + 74*x^91 + 56*x^90 + 19*x^89 + 104*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 40*x^82 + 123*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 45*x^73 + 120*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 56*x^66 + 13*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 95*x^25 + 8*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 72*x^18 + 7*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 105*x^9 + 24*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 88*x^2 + 41*x + 8, x^93 + 74*x^91 + 60*x^90 + 107*x^89 + 44*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 84*x^82 + 99*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 53*x^73 + 100*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 28*x^66 + 69*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 23*x^25 + 28*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 100*x^18 + 15*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 81*x^9 + 84*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 44*x^2 + x + 60, x^93 + 74*x^91 + 112*x^90 + 35*x^89 + 16*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 80*x^82 + 107*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 93*x^73 + 48*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 112*x^66 + 93*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 47*x^25 + 80*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 16*x^18 + 55*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 89*x^9 + 112*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 48*x^2 + 57*x + 80, x^93 + 74*x^91 + 44*x^90 + 91*x^89 + 44*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 36*x^82 + 115*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 5*x^73 + 100*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 12*x^66 + 117*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 71*x^25 + 28*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 116*x^18 + 95*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 97*x^9 + 84*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 92*x^2 + 113*x + 60, x^93 + 74*x^91 + 8*x^90 + 83*x^89 + 120*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 88*x^82 + 123*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 109*x^73 + 40*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 72*x^66 + 13*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 31*x^25 + 88*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 56*x^18 + 7*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 41*x^9 + 8*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 40*x^2 + 41*x + 24, x^93 + 74*x^91 + 104*x^90 + 51*x^89 + 24*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 120*x^82 + 27*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 13*x^73 + 8*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 40*x^66 + 109*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 127*x^25 + 120*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 88*x^18 + 39*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 73*x^9 + 104*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 8*x^2 + 9*x + 56, x^93 + 74*x^91 + 80*x^90 + 51*x^89 + 32*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 38*x^83 + 48*x^82 + 27*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 13*x^73 + 96*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 50*x^67 + 16*x^66 + 109*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 127*x^25 + 32*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 94*x^19 + 112*x^18 + 39*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 73*x^9 + 96*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 42*x^3 + 80*x^2 + 9*x + 96, x^93 + 74*x^91 + 60*x^90 + 43*x^89 + 108*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 84*x^82 + 35*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 117*x^73 + 36*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 28*x^66 + 5*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 87*x^25 + 92*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 100*x^18 + 79*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 17*x^9 + 20*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 44*x^2 + 65*x + 124, x^93 + 74*x^91 + 12*x^90 + 43*x^89 + 60*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 4*x^82 + 99*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 117*x^73 + 20*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 44*x^66 + 69*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 87*x^25 + 108*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 84*x^18 + 15*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 17*x^9 + 68*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 124*x^2 + x + 76, x^93 + 74*x^91 + 124*x^90 + 59*x^89 + 124*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 20*x^82 + 19*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 37*x^73 + 84*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 92*x^66 + 85*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 39*x^25 + 44*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 36*x^18 + 127*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + x^9 + 4*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 108*x^2 + 81*x + 76, x^93 + 74*x^91 + 16*x^90 + 51*x^89 + 64*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 102*x^83 + 48*x^82 + 91*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 13*x^73 + 64*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 114*x^67 + 16*x^66 + 45*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 127*x^25 + 64*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 30*x^19 + 112*x^18 + 103*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 73*x^9 + 64*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 106*x^3 + 80*x^2 + 73*x + 64, x^93 + 74*x^91 + 84*x^90 + 43*x^89 + 100*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 28*x^82 + 99*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 117*x^73 + 76*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 52*x^66 + 69*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 87*x^25 + 52*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 76*x^18 + 15*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 17*x^9 + 28*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 100*x^2 + x + 84, x^93 + 74*x^91 + 36*x^90 + 59*x^89 + 4*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 76*x^82 + 19*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 37*x^73 + 44*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 68*x^66 + 85*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 39*x^25 + 84*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 60*x^18 + 127*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + x^9 + 124*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 52*x^2 + 81*x + 52, x^93 + 74*x^91 + 56*x^90 + 67*x^89 + 56*x^88 + 4*x^87 + 16*x^86 + x^85 + 80*x^84 + 38*x^83 + 40*x^82 + 75*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 61*x^73 + 104*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 56*x^66 + 125*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 79*x^25 + 24*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 72*x^18 + 23*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 57*x^9 + 72*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 88*x^2 + 89*x + 24, x^93 + 74*x^91 + 24*x^90 + 67*x^89 + 88*x^88 + 4*x^87 + 80*x^86 + x^85 + 16*x^84 + 38*x^83 + 72*x^82 + 75*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 61*x^73 + 72*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 24*x^66 + 125*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 79*x^25 + 56*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 104*x^18 + 23*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 57*x^9 + 40*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 56*x^2 + 89*x + 56, x^93 + 74*x^91 + 24*x^90 + 83*x^89 + 72*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 8*x^82 + 123*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 109*x^73 + 24*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 88*x^66 + 13*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 31*x^25 + 104*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 40*x^18 + 7*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 41*x^9 + 56*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 120*x^2 + 41*x + 40, x^93 + 74*x^91 + 72*x^90 + 67*x^89 + 72*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 24*x^82 + 11*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 61*x^73 + 24*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 8*x^66 + 61*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 79*x^25 + 104*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 120*x^18 + 87*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 57*x^9 + 56*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 104*x^2 + 25*x + 40, x^93 + 74*x^91 + 16*x^90 + 51*x^89 + 32*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 48*x^82 + 91*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 13*x^73 + 96*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 16*x^66 + 45*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 127*x^25 + 32*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 112*x^18 + 103*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 73*x^9 + 96*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 80*x^2 + 73*x + 32, x^93 + 74*x^91 + 115*x^89 + 16*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 38*x^83 + 64*x^82 + 91*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 77*x^73 + 48*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 50*x^67 + 64*x^66 + 45*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 63*x^25 + 80*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 94*x^19 + 64*x^18 + 103*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 9*x^9 + 112*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 42*x^3 + 64*x^2 + 73*x + 16, x^93 + 74*x^91 + 108*x^90 + 91*x^89 + 12*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 100*x^82 + 115*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 5*x^73 + 4*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 76*x^66 + 117*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 71*x^25 + 124*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 52*x^18 + 95*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 97*x^9 + 116*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 28*x^2 + 113*x + 28, x^93 + 74*x^91 + 16*x^90 + 115*x^89 + 96*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 38*x^83 + 112*x^82 + 91*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 77*x^73 + 32*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 50*x^67 + 80*x^66 + 45*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 63*x^25 + 96*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 94*x^19 + 48*x^18 + 103*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 9*x^9 + 32*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 42*x^3 + 16*x^2 + 73*x + 32, x^93 + 74*x^91 + 88*x^90 + 51*x^89 + 104*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 38*x^83 + 72*x^82 + 27*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 13*x^73 + 120*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 50*x^67 + 24*x^66 + 109*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 127*x^25 + 8*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 94*x^19 + 104*x^18 + 39*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 73*x^9 + 24*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 42*x^3 + 56*x^2 + 9*x + 72, x^93 + 74*x^91 + 4*x^90 + 43*x^89 + 52*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 108*x^82 + 35*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 117*x^73 + 60*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 36*x^66 + 5*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 87*x^25 + 68*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 92*x^18 + 79*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 17*x^9 + 76*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 20*x^2 + 65*x + 36, x^93 + 74*x^91 + 108*x^90 + 59*x^89 + 44*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 100*x^82 + 19*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 37*x^73 + 100*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 76*x^66 + 85*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 39*x^25 + 28*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 52*x^18 + 127*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + x^9 + 84*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 28*x^2 + 81*x + 60, x^93 + 74*x^91 + 32*x^90 + 67*x^89 + 64*x^88 + 4*x^87 + 64*x^86 + x^85 + 38*x^83 + 96*x^82 + 75*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 61*x^73 + 64*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 50*x^67 + 32*x^66 + 125*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 79*x^25 + 64*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 94*x^19 + 96*x^18 + 23*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 57*x^9 + 64*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 42*x^3 + 32*x^2 + 89*x + 64, x^93 + 74*x^91 + 115*x^89 + 48*x^88 + 68*x^87 + 97*x^85 + 32*x^84 + 102*x^83 + 27*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 77*x^73 + 16*x^72 + 116*x^71 + 103*x^69 + 32*x^68 + 114*x^67 + 109*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 63*x^25 + 112*x^24 + 116*x^23 + 5*x^21 + 32*x^20 + 30*x^19 + 39*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 9*x^9 + 80*x^8 + 68*x^7 + 123*x^5 + 32*x^4 + 106*x^3 + 9*x + 112, x^93 + 74*x^91 + 100*x^90 + 11*x^89 + 52*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 12*x^82 + 67*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 21*x^73 + 60*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 4*x^66 + 101*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 55*x^25 + 68*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 124*x^18 + 111*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 49*x^9 + 76*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 116*x^2 + 33*x + 36, x^93 + 74*x^91 + 44*x^90 + 11*x^89 + 124*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 36*x^82 + 67*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 21*x^73 + 84*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 12*x^66 + 101*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 55*x^25 + 44*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 116*x^18 + 111*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 49*x^9 + 4*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 92*x^2 + 33*x + 76, x^93 + 74*x^91 + 16*x^90 + 35*x^89 + 16*x^88 + 68*x^87 + 32*x^86 + x^85 + 32*x^84 + 102*x^83 + 112*x^82 + 43*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 93*x^73 + 48*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 80*x^66 + 29*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 47*x^25 + 80*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 48*x^18 + 119*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 89*x^9 + 112*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 16*x^2 + 121*x + 16, x^93 + 74*x^91 + 124*x^90 + 27*x^89 + 124*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 20*x^82 + 51*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 69*x^73 + 84*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 92*x^66 + 53*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 7*x^25 + 44*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 36*x^18 + 31*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 33*x^9 + 4*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 108*x^2 + 49*x + 76, x^93 + 74*x^91 + 4*x^90 + 91*x^89 + 36*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 44*x^82 + 51*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 5*x^73 + 12*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 100*x^66 + 53*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 71*x^25 + 116*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 28*x^18 + 31*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 97*x^9 + 92*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 84*x^2 + 49*x + 20, x^93 + 74*x^91 + 56*x^90 + 19*x^89 + 40*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 40*x^82 + 123*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 45*x^73 + 56*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 56*x^66 + 13*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 95*x^25 + 72*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 72*x^18 + 7*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 105*x^9 + 88*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 88*x^2 + 41*x + 72, x^93 + 74*x^91 + 44*x^90 + 59*x^89 + 108*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 100*x^82 + 83*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 37*x^73 + 36*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 76*x^66 + 21*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 39*x^25 + 92*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 52*x^18 + 63*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + x^9 + 20*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 28*x^2 + 17*x + 60, x^93 + 74*x^91 + 112*x^90 + 35*x^89 + 80*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 80*x^82 + 107*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 93*x^73 + 112*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 112*x^66 + 93*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 47*x^25 + 16*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 16*x^18 + 55*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 89*x^9 + 48*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 48*x^2 + 57*x + 16, x^93 + 74*x^91 + 72*x^90 + 115*x^89 + 24*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 24*x^82 + 91*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 77*x^73 + 8*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 8*x^66 + 45*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 63*x^25 + 120*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 120*x^18 + 103*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 9*x^9 + 104*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 104*x^2 + 73*x + 56, x^93 + 74*x^91 + 112*x^90 + 115*x^89 + 64*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 16*x^82 + 91*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 77*x^73 + 64*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 48*x^66 + 45*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 63*x^25 + 64*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 80*x^18 + 103*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 9*x^9 + 64*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 112*x^2 + 73*x, x^93 + 74*x^91 + 120*x^90 + 51*x^89 + 8*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 40*x^82 + 27*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 13*x^73 + 88*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 56*x^66 + 109*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 127*x^25 + 40*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 72*x^18 + 39*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 73*x^9 + 120*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 88*x^2 + 9*x + 104, x^93 + 74*x^91 + 88*x^90 + 35*x^89 + 120*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 8*x^82 + 107*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 93*x^73 + 40*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 88*x^66 + 93*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 47*x^25 + 88*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 40*x^18 + 55*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 89*x^9 + 8*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 120*x^2 + 57*x + 88, x^93 + 74*x^91 + 68*x^90 + 11*x^89 + 84*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 108*x^82 + 3*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 21*x^73 + 28*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 36*x^66 + 37*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 55*x^25 + 100*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 92*x^18 + 47*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 49*x^9 + 44*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 20*x^2 + 97*x + 4, x^93 + 74*x^91 + 104*x^90 + 51*x^89 + 56*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 56*x^82 + 91*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 13*x^73 + 104*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 104*x^66 + 45*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 127*x^25 + 24*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 24*x^18 + 103*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 73*x^9 + 72*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 72*x^2 + 73*x + 24, x^93 + 74*x^91 + 72*x^90 + 19*x^89 + 24*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 88*x^82 + 123*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 45*x^73 + 8*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 72*x^66 + 13*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 95*x^25 + 120*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 56*x^18 + 7*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 105*x^9 + 104*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 40*x^2 + 41*x + 120, x^93 + 74*x^91 + 4*x^90 + 59*x^89 + 4*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 44*x^82 + 83*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 37*x^73 + 44*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 100*x^66 + 21*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 39*x^25 + 84*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 28*x^18 + 63*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + x^9 + 124*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 84*x^2 + 17*x + 116, x^93 + 74*x^91 + 36*x^90 + 43*x^89 + 52*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 76*x^82 + 35*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 117*x^73 + 60*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 68*x^66 + 5*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 87*x^25 + 68*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 60*x^18 + 79*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 17*x^9 + 76*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 52*x^2 + 65*x + 36, x^93 + 74*x^91 + 84*x^90 + 107*x^89 + 100*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 28*x^82 + 35*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 53*x^73 + 76*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 52*x^66 + 5*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 23*x^25 + 52*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 76*x^18 + 79*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 81*x^9 + 28*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 100*x^2 + 65*x + 84, x^93 + 74*x^91 + 96*x^90 + 19*x^89 + 80*x^88 + 4*x^87 + 97*x^85 + 32*x^84 + 38*x^83 + 96*x^82 + 59*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 45*x^73 + 112*x^72 + 52*x^71 + 103*x^69 + 32*x^68 + 50*x^67 + 32*x^66 + 77*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 95*x^25 + 16*x^24 + 52*x^23 + 5*x^21 + 32*x^20 + 94*x^19 + 96*x^18 + 71*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 105*x^9 + 48*x^8 + 4*x^7 + 123*x^5 + 32*x^4 + 42*x^3 + 32*x^2 + 105*x + 80, x^93 + 74*x^91 + 56*x^90 + 35*x^89 + 56*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 40*x^82 + 107*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 93*x^73 + 104*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 56*x^66 + 93*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 47*x^25 + 24*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 72*x^18 + 55*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 89*x^9 + 72*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 88*x^2 + 57*x + 24, x^93 + 74*x^91 + 72*x^90 + 67*x^89 + 104*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 24*x^82 + 11*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 61*x^73 + 120*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 8*x^66 + 61*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 79*x^25 + 8*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 120*x^18 + 87*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 57*x^9 + 24*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 104*x^2 + 25*x + 72, x^93 + 74*x^91 + 92*x^90 + 27*x^89 + 60*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 116*x^82 + 115*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 69*x^73 + 20*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 124*x^66 + 117*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 7*x^25 + 108*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 4*x^18 + 95*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 33*x^9 + 68*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 12*x^2 + 113*x + 76, x^93 + 74*x^91 + 28*x^90 + 43*x^89 + 44*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 116*x^82 + 35*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 117*x^73 + 100*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 124*x^66 + 5*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 87*x^25 + 28*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 4*x^18 + 79*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 17*x^9 + 84*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 12*x^2 + 65*x + 60, x^93 + 74*x^91 + 16*x^90 + 19*x^89 + 96*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 38*x^83 + 112*x^82 + 59*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 45*x^73 + 32*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 50*x^67 + 80*x^66 + 77*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 95*x^25 + 96*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 94*x^19 + 48*x^18 + 71*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 105*x^9 + 32*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 42*x^3 + 16*x^2 + 105*x + 32, x^93 + 74*x^91 + 8*x^90 + 99*x^89 + 40*x^88 + 68*x^87 + 48*x^86 + x^85 + 48*x^84 + 102*x^83 + 88*x^82 + 107*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 29*x^73 + 56*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 72*x^66 + 93*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 111*x^25 + 72*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 56*x^18 + 55*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 25*x^9 + 88*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 40*x^2 + 57*x + 8, x^93 + 74*x^91 + 84*x^90 + 123*x^89 + 84*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 92*x^82 + 83*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 101*x^73 + 28*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 116*x^66 + 21*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 103*x^25 + 100*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 12*x^18 + 63*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 65*x^9 + 44*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 36*x^2 + 17*x + 68, x^93 + 74*x^91 + 115*x^89 + 112*x^88 + 68*x^87 + 97*x^85 + 32*x^84 + 102*x^83 + 27*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 77*x^73 + 80*x^72 + 116*x^71 + 103*x^69 + 32*x^68 + 114*x^67 + 109*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 63*x^25 + 48*x^24 + 116*x^23 + 5*x^21 + 32*x^20 + 30*x^19 + 39*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 9*x^9 + 16*x^8 + 68*x^7 + 123*x^5 + 32*x^4 + 106*x^3 + 9*x + 48, x^93 + 74*x^91 + 100*x^90 + 43*x^89 + 84*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 76*x^82 + 99*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 117*x^73 + 28*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 68*x^66 + 69*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 87*x^25 + 100*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 60*x^18 + 15*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 17*x^9 + 44*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 52*x^2 + x + 4, x^93 + 74*x^91 + 24*x^90 + 115*x^89 + 8*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 8*x^82 + 91*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 77*x^73 + 88*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 88*x^66 + 45*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 63*x^25 + 40*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 40*x^18 + 103*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 9*x^9 + 120*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 120*x^2 + 73*x + 104, x^93 + 74*x^91 + 60*x^90 + 123*x^89 + 28*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 84*x^82 + 83*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 101*x^73 + 52*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 28*x^66 + 21*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 103*x^25 + 76*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 100*x^18 + 63*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 65*x^9 + 100*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 44*x^2 + 17*x + 108, x^93 + 74*x^91 + 16*x^90 + 67*x^89 + 112*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 112*x^82 + 11*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 61*x^73 + 80*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 80*x^66 + 61*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 79*x^25 + 48*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 48*x^18 + 87*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 57*x^9 + 16*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 16*x^2 + 25*x + 112, x^93 + 74*x^91 + 100*x^90 + 27*x^89 + 36*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 76*x^82 + 115*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 69*x^73 + 12*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 68*x^66 + 117*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 7*x^25 + 116*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 60*x^18 + 95*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 33*x^9 + 92*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 52*x^2 + 113*x + 20, x^93 + 74*x^91 + 120*x^90 + 3*x^89 + 120*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 40*x^82 + 75*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 125*x^73 + 40*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 56*x^66 + 125*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 15*x^25 + 88*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 72*x^18 + 23*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 121*x^9 + 8*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 88*x^2 + 89*x + 24, x^93 + 74*x^91 + 100*x^90 + 91*x^89 + 36*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 12*x^82 + 115*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 5*x^73 + 12*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 4*x^66 + 117*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 71*x^25 + 116*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 124*x^18 + 95*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 97*x^9 + 92*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 116*x^2 + 113*x + 84, x^93 + 74*x^91 + 56*x^90 + 35*x^89 + 88*x^88 + 68*x^87 + 80*x^86 + x^85 + 80*x^84 + 102*x^83 + 104*x^82 + 43*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 93*x^73 + 72*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 120*x^66 + 29*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 47*x^25 + 56*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 8*x^18 + 119*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 89*x^9 + 40*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 24*x^2 + 121*x + 120, x^93 + 74*x^91 + 36*x^90 + 91*x^89 + 68*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 76*x^82 + 115*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 5*x^73 + 108*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 68*x^66 + 117*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 71*x^25 + 20*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 60*x^18 + 95*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 97*x^9 + 60*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 52*x^2 + 113*x + 116, x^93 + 74*x^91 + 12*x^90 + 91*x^89 + 12*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 68*x^82 + 115*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 5*x^73 + 4*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 108*x^66 + 117*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 71*x^25 + 124*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 20*x^18 + 95*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 97*x^9 + 116*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 60*x^2 + 113*x + 28, x^93 + 74*x^91 + 48*x^90 + 67*x^89 + 16*x^88 + 4*x^87 + 32*x^86 + x^85 + 96*x^84 + 38*x^83 + 16*x^82 + 75*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 61*x^73 + 48*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 48*x^66 + 125*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 79*x^25 + 80*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 80*x^18 + 23*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 57*x^9 + 112*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 112*x^2 + 89*x + 80, x^93 + 74*x^91 + 64*x^90 + 3*x^89 + 4*x^87 + x^85 + 38*x^83 + 64*x^82 + 11*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 125*x^73 + 52*x^71 + 7*x^69 + 50*x^67 + 64*x^66 + 61*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 15*x^25 + 52*x^23 + 37*x^21 + 94*x^19 + 64*x^18 + 87*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 121*x^9 + 4*x^7 + 27*x^5 + 42*x^3 + 64*x^2 + 25*x, x^93 + 74*x^91 + 108*x^90 + 27*x^89 + 44*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 36*x^82 + 115*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 69*x^73 + 100*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 12*x^66 + 117*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 7*x^25 + 28*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 116*x^18 + 95*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 33*x^9 + 84*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 92*x^2 + 113*x + 124, x^93 + 74*x^91 + 48*x^90 + 19*x^89 + 64*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 80*x^82 + 59*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 45*x^73 + 64*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 112*x^66 + 77*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 95*x^25 + 64*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 16*x^18 + 71*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 105*x^9 + 64*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 48*x^2 + 105*x, x^93 + 74*x^91 + 8*x^90 + 19*x^89 + 88*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 24*x^82 + 123*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 45*x^73 + 72*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 8*x^66 + 13*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 95*x^25 + 56*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 120*x^18 + 7*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 105*x^9 + 40*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 104*x^2 + 41*x + 56, x^93 + 74*x^91 + 32*x^90 + 99*x^89 + 4*x^87 + 64*x^86 + 65*x^85 + 38*x^83 + 96*x^82 + 43*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 29*x^73 + 52*x^71 + 64*x^70 + 71*x^69 + 50*x^67 + 32*x^66 + 29*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 111*x^25 + 52*x^23 + 64*x^22 + 101*x^21 + 94*x^19 + 96*x^18 + 119*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 25*x^9 + 4*x^7 + 64*x^6 + 91*x^5 + 42*x^3 + 32*x^2 + 121*x, x^93 + 74*x^91 + 40*x^90 + 115*x^89 + 56*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 56*x^82 + 91*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 77*x^73 + 104*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 104*x^66 + 45*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 63*x^25 + 24*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 24*x^18 + 103*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 9*x^9 + 72*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 72*x^2 + 73*x + 88, x^93 + 74*x^91 + 112*x^90 + 99*x^89 + 16*x^88 + 68*x^87 + 96*x^86 + x^85 + 32*x^84 + 102*x^83 + 16*x^82 + 107*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 29*x^73 + 48*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 114*x^67 + 48*x^66 + 93*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 111*x^25 + 80*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 30*x^19 + 80*x^18 + 55*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 25*x^9 + 112*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 106*x^3 + 112*x^2 + 57*x + 16, x^93 + 74*x^91 + 36*x^90 + 123*x^89 + 100*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 12*x^82 + 19*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 101*x^73 + 76*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 4*x^66 + 85*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 103*x^25 + 52*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 124*x^18 + 127*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 65*x^9 + 28*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 116*x^2 + 81*x + 84, x^93 + 74*x^91 + 116*x^90 + 59*x^89 + 84*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 124*x^82 + 83*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 37*x^73 + 28*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 84*x^66 + 21*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 39*x^25 + 100*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 44*x^18 + 63*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + x^9 + 44*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 4*x^2 + 17*x + 4, x^93 + 74*x^91 + 44*x^90 + 107*x^89 + 92*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 100*x^82 + 35*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 53*x^73 + 116*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 76*x^66 + 5*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 23*x^25 + 12*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 52*x^18 + 79*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 81*x^9 + 36*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 28*x^2 + 65*x + 108, x^93 + 74*x^91 + 64*x^90 + 35*x^89 + 32*x^88 + 4*x^87 + 65*x^85 + 64*x^84 + 38*x^83 + 64*x^82 + 107*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 93*x^73 + 96*x^72 + 52*x^71 + 71*x^69 + 64*x^68 + 50*x^67 + 64*x^66 + 93*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 47*x^25 + 32*x^24 + 52*x^23 + 101*x^21 + 64*x^20 + 94*x^19 + 64*x^18 + 55*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 89*x^9 + 96*x^8 + 4*x^7 + 91*x^5 + 64*x^4 + 42*x^3 + 64*x^2 + 57*x + 32, x^93 + 74*x^91 + 96*x^90 + 19*x^89 + 48*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 102*x^83 + 32*x^82 + 123*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 45*x^73 + 16*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 114*x^67 + 96*x^66 + 13*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 95*x^25 + 112*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 30*x^19 + 32*x^18 + 7*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 105*x^9 + 80*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 106*x^3 + 96*x^2 + 41*x + 112, x^93 + 74*x^91 + 12*x^90 + 43*x^89 + 28*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 4*x^82 + 99*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 117*x^73 + 52*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 44*x^66 + 69*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 87*x^25 + 76*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 84*x^18 + 15*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 17*x^9 + 100*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 124*x^2 + x + 44, x^93 + 74*x^91 + 100*x^90 + 123*x^89 + 68*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 76*x^82 + 19*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 101*x^73 + 108*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 68*x^66 + 85*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 103*x^25 + 20*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 60*x^18 + 127*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 65*x^9 + 60*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 52*x^2 + 81*x + 52, x^93 + 74*x^91 + 44*x^90 + 11*x^89 + 60*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 36*x^82 + 67*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 21*x^73 + 20*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 12*x^66 + 101*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 55*x^25 + 108*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 116*x^18 + 111*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 49*x^9 + 68*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 92*x^2 + 33*x + 12, x^93 + 74*x^91 + 120*x^90 + 19*x^89 + 8*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 104*x^82 + 123*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 45*x^73 + 88*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 120*x^66 + 13*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 95*x^25 + 40*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 8*x^18 + 7*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 105*x^9 + 120*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 24*x^2 + 41*x + 40, x^93 + 74*x^91 + 80*x^90 + 19*x^89 + 96*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 112*x^82 + 123*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 45*x^73 + 32*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 80*x^66 + 13*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 95*x^25 + 96*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 48*x^18 + 7*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 105*x^9 + 32*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 16*x^2 + 41*x + 96, x^93 + 74*x^91 + 44*x^90 + 123*x^89 + 12*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 36*x^82 + 83*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 101*x^73 + 4*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 12*x^66 + 21*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 103*x^25 + 124*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 116*x^18 + 63*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 65*x^9 + 116*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 92*x^2 + 17*x + 28, x^93 + 74*x^91 + 35*x^89 + 96*x^88 + 68*x^87 + 64*x^86 + x^85 + 102*x^83 + 64*x^82 + 43*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 93*x^73 + 32*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 114*x^67 + 64*x^66 + 29*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 47*x^25 + 96*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 30*x^19 + 64*x^18 + 119*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 89*x^9 + 32*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 106*x^3 + 64*x^2 + 121*x + 32, x^93 + 74*x^91 + 44*x^90 + 91*x^89 + 76*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 100*x^82 + 51*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 5*x^73 + 68*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 76*x^66 + 53*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 71*x^25 + 60*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 52*x^18 + 31*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 97*x^9 + 52*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 28*x^2 + 49*x + 28, x^93 + 74*x^91 + 40*x^90 + 99*x^89 + 40*x^88 + 68*x^87 + 112*x^86 + x^85 + 48*x^84 + 102*x^83 + 56*x^82 + 107*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 29*x^73 + 56*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 104*x^66 + 93*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 111*x^25 + 72*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 24*x^18 + 55*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 25*x^9 + 88*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 72*x^2 + 57*x + 8, x^93 + 74*x^91 + 4*x^90 + 11*x^89 + 52*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 108*x^82 + 67*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 21*x^73 + 60*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 36*x^66 + 101*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 55*x^25 + 68*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 92*x^18 + 111*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 49*x^9 + 76*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 20*x^2 + 33*x + 36, x^93 + 74*x^91 + 12*x^90 + 75*x^89 + 92*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 68*x^82 + 3*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 85*x^73 + 116*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 108*x^66 + 37*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 119*x^25 + 12*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 20*x^18 + 47*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 113*x^9 + 36*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 60*x^2 + 97*x + 44, x^93 + 74*x^91 + 64*x^90 + 19*x^89 + 112*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 96*x^84 + 38*x^83 + 59*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 45*x^73 + 80*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 96*x^68 + 50*x^67 + 77*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 95*x^25 + 48*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 96*x^20 + 94*x^19 + 71*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 105*x^9 + 16*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 96*x^4 + 42*x^3 + 105*x + 112, x^93 + 74*x^91 + 124*x^90 + 59*x^89 + 28*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 20*x^82 + 19*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 37*x^73 + 52*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 92*x^66 + 85*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 39*x^25 + 76*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 36*x^18 + 127*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + x^9 + 100*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 108*x^2 + 81*x + 108, x^93 + 74*x^91 + 24*x^90 + 35*x^89 + 56*x^88 + 68*x^87 + 16*x^86 + x^85 + 16*x^84 + 102*x^83 + 8*x^82 + 43*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 93*x^73 + 104*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 88*x^66 + 29*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 47*x^25 + 24*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 40*x^18 + 119*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 89*x^9 + 72*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 120*x^2 + 121*x + 88, x^93 + 74*x^91 + 40*x^90 + 19*x^89 + 88*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 56*x^82 + 59*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 45*x^73 + 72*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 104*x^66 + 77*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 95*x^25 + 56*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 24*x^18 + 71*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 105*x^9 + 40*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 72*x^2 + 105*x + 120, x^93 + 74*x^91 + 112*x^90 + 99*x^89 + 112*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 80*x^82 + 43*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 29*x^73 + 80*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 112*x^66 + 29*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 111*x^25 + 48*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 16*x^18 + 119*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 25*x^9 + 16*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 48*x^2 + 121*x + 48, x^93 + 74*x^91 + 36*x^90 + 59*x^89 + 36*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 12*x^82 + 83*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 37*x^73 + 12*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 4*x^66 + 21*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 39*x^25 + 116*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 124*x^18 + 63*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + x^9 + 92*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 116*x^2 + 17*x + 20, x^93 + 74*x^91 + 16*x^90 + 3*x^89 + 48*x^88 + 4*x^87 + 96*x^86 + x^85 + 32*x^84 + 38*x^83 + 48*x^82 + 11*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 125*x^73 + 16*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 16*x^66 + 61*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 15*x^25 + 112*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 112*x^18 + 87*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 121*x^9 + 80*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 80*x^2 + 25*x + 112, x^93 + 74*x^91 + 120*x^90 + 83*x^89 + 104*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 104*x^82 + 59*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 109*x^73 + 120*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 120*x^66 + 77*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 31*x^25 + 8*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 8*x^18 + 71*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 41*x^9 + 24*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 24*x^2 + 105*x + 8, x^93 + 74*x^91 + 124*x^90 + 75*x^89 + 12*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 20*x^82 + 3*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 85*x^73 + 4*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 92*x^66 + 37*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 119*x^25 + 124*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 36*x^18 + 47*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 113*x^9 + 116*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 108*x^2 + 97*x + 28, x^93 + 74*x^91 + 112*x^90 + 67*x^89 + 80*x^88 + 4*x^87 + 32*x^86 + x^85 + 96*x^84 + 38*x^83 + 80*x^82 + 75*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 61*x^73 + 112*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 112*x^66 + 125*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 79*x^25 + 16*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 16*x^18 + 23*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 57*x^9 + 48*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 48*x^2 + 89*x + 16, x^93 + 74*x^91 + 60*x^90 + 75*x^89 + 12*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 84*x^82 + 3*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 85*x^73 + 4*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 28*x^66 + 37*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 119*x^25 + 124*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 100*x^18 + 47*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 113*x^9 + 116*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 44*x^2 + 97*x + 28, x^93 + 74*x^91 + 44*x^90 + 43*x^89 + 28*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 100*x^82 + 99*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 117*x^73 + 52*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 76*x^66 + 69*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 87*x^25 + 76*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 52*x^18 + 15*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 17*x^9 + 100*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 28*x^2 + x + 44, x^93 + 74*x^91 + 8*x^90 + 83*x^89 + 24*x^88 + 68*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 24*x^82 + 59*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 109*x^73 + 8*x^72 + 116*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 8*x^66 + 77*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 31*x^25 + 120*x^24 + 116*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 120*x^18 + 71*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 41*x^9 + 104*x^8 + 68*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 104*x^2 + 105*x + 120, x^93 + 74*x^91 + 16*x^90 + 115*x^89 + 64*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 112*x^82 + 91*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 77*x^73 + 64*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 80*x^66 + 45*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 63*x^25 + 64*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 48*x^18 + 103*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 9*x^9 + 64*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 16*x^2 + 73*x, x^93 + 74*x^91 + 72*x^90 + 51*x^89 + 56*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 24*x^82 + 27*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 13*x^73 + 104*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 8*x^66 + 109*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 127*x^25 + 24*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 120*x^18 + 39*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 73*x^9 + 72*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 104*x^2 + 9*x + 88, x^93 + 74*x^91 + 116*x^90 + 75*x^89 + 100*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 124*x^82 + 67*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 85*x^73 + 76*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 84*x^66 + 101*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 119*x^25 + 52*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 44*x^18 + 111*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 113*x^9 + 28*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 4*x^2 + 33*x + 84, x^93 + 74*x^91 + 112*x^90 + 51*x^89 + 96*x^88 + 68*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 80*x^82 + 91*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 13*x^73 + 32*x^72 + 116*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 112*x^66 + 45*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 127*x^25 + 96*x^24 + 116*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 16*x^18 + 103*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 73*x^9 + 32*x^8 + 68*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 48*x^2 + 73*x + 96, x^93 + 74*x^91 + 112*x^90 + 83*x^89 + 96*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 80*x^82 + 59*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 109*x^73 + 32*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 112*x^66 + 77*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 31*x^25 + 96*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 16*x^18 + 71*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 41*x^9 + 32*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 48*x^2 + 105*x + 96, x^93 + 74*x^91 + 72*x^90 + 35*x^89 + 104*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 88*x^82 + 107*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 93*x^73 + 120*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 72*x^66 + 93*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 47*x^25 + 8*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 56*x^18 + 55*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 89*x^9 + 24*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 40*x^2 + 57*x + 8, x^93 + 74*x^91 + 28*x^90 + 11*x^89 + 12*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 116*x^82 + 67*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 21*x^73 + 4*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 124*x^66 + 101*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 55*x^25 + 124*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 4*x^18 + 111*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 49*x^9 + 116*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 12*x^2 + 33*x + 28, x^93 + 74*x^91 + 20*x^90 + 43*x^89 + 4*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 28*x^82 + 35*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 117*x^73 + 44*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 52*x^66 + 5*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 87*x^25 + 84*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 76*x^18 + 79*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 17*x^9 + 124*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 100*x^2 + 65*x + 52, x^93 + 74*x^91 + 96*x^90 + 51*x^89 + 16*x^88 + 4*x^87 + 33*x^85 + 32*x^84 + 38*x^83 + 96*x^82 + 27*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 13*x^73 + 48*x^72 + 52*x^71 + 39*x^69 + 32*x^68 + 50*x^67 + 32*x^66 + 109*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 127*x^25 + 80*x^24 + 52*x^23 + 69*x^21 + 32*x^20 + 94*x^19 + 96*x^18 + 39*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 73*x^9 + 112*x^8 + 4*x^7 + 59*x^5 + 32*x^4 + 42*x^3 + 32*x^2 + 9*x + 16, x^93 + 74*x^91 + 24*x^90 + 19*x^89 + 40*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 72*x^82 + 123*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 45*x^73 + 56*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 24*x^66 + 13*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 95*x^25 + 72*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 104*x^18 + 7*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 105*x^9 + 88*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 56*x^2 + 41*x + 72, x^93 + 74*x^91 + 60*x^90 + 27*x^89 + 92*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 84*x^82 + 51*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 69*x^73 + 116*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 28*x^66 + 53*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 7*x^25 + 12*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 100*x^18 + 31*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 33*x^9 + 36*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 44*x^2 + 49*x + 44, x^93 + 74*x^91 + 88*x^90 + 67*x^89 + 56*x^88 + 4*x^87 + 80*x^86 + x^85 + 80*x^84 + 38*x^83 + 8*x^82 + 75*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 61*x^73 + 104*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 88*x^66 + 125*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 79*x^25 + 24*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 40*x^18 + 23*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 57*x^9 + 72*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 120*x^2 + 89*x + 24, x^93 + 74*x^91 + 108*x^90 + 27*x^89 + 12*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 100*x^82 + 51*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 69*x^73 + 4*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 76*x^66 + 53*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 7*x^25 + 124*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 52*x^18 + 31*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 33*x^9 + 116*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 28*x^2 + 49*x + 28, x^93 + 74*x^91 + 36*x^90 + 107*x^89 + 52*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 12*x^82 + 35*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 53*x^73 + 60*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 4*x^66 + 5*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 23*x^25 + 68*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 124*x^18 + 79*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 81*x^9 + 76*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 116*x^2 + 65*x + 100, x^93 + 74*x^91 + 92*x^90 + 27*x^89 + 28*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 116*x^82 + 115*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 69*x^73 + 52*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 124*x^66 + 117*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 7*x^25 + 76*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 4*x^18 + 95*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 33*x^9 + 100*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 12*x^2 + 113*x + 44, x^93 + 74*x^91 + 104*x^90 + 35*x^89 + 104*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 56*x^82 + 107*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 93*x^73 + 120*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 104*x^66 + 93*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 47*x^25 + 8*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 24*x^18 + 55*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 89*x^9 + 24*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 72*x^2 + 57*x + 8, x^93 + 74*x^91 + 12*x^90 + 59*x^89 + 12*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 4*x^82 + 83*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 37*x^73 + 4*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 44*x^66 + 21*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 39*x^25 + 124*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 84*x^18 + 63*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + x^9 + 116*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 124*x^2 + 17*x + 92, x^93 + 74*x^91 + 84*x^90 + 59*x^89 + 20*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 92*x^82 + 19*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 37*x^73 + 92*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 116*x^66 + 85*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 39*x^25 + 36*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 12*x^18 + 127*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + x^9 + 108*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 36*x^2 + 81*x + 4, x^93 + 74*x^91 + 12*x^90 + 91*x^89 + 108*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 68*x^82 + 115*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 5*x^73 + 36*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 108*x^66 + 117*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 71*x^25 + 92*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 20*x^18 + 95*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 97*x^9 + 20*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 60*x^2 + 113*x + 124, x^93 + 74*x^91 + 68*x^90 + 75*x^89 + 84*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 44*x^82 + 3*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 85*x^73 + 28*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 100*x^66 + 37*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 119*x^25 + 100*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 28*x^18 + 47*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 113*x^9 + 44*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 84*x^2 + 97*x + 68, x^93 + 74*x^91 + 64*x^90 + 51*x^89 + 80*x^88 + 4*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 38*x^83 + 27*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 13*x^73 + 112*x^72 + 52*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 50*x^67 + 109*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 127*x^25 + 16*x^24 + 52*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 94*x^19 + 39*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 73*x^9 + 48*x^8 + 4*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 42*x^3 + 9*x + 80, x^93 + 74*x^91 + 72*x^90 + 99*x^89 + 40*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 88*x^82 + 43*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 29*x^73 + 56*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 72*x^66 + 29*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 111*x^25 + 72*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 56*x^18 + 119*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 25*x^9 + 88*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 40*x^2 + 121*x + 72, x^93 + 74*x^91 + 20*x^90 + 75*x^89 + 68*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 92*x^82 + 67*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 85*x^73 + 108*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 116*x^66 + 101*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 119*x^25 + 20*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 12*x^18 + 111*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 113*x^9 + 60*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 36*x^2 + 33*x + 52, x^93 + 74*x^91 + 28*x^90 + 123*x^89 + 124*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 52*x^82 + 19*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 101*x^73 + 84*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 60*x^66 + 85*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 103*x^25 + 44*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 68*x^18 + 127*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 65*x^9 + 4*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 76*x^2 + 81*x + 12, x^93 + 74*x^91 + 76*x^90 + 75*x^89 + 124*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 68*x^82 + 67*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 85*x^73 + 84*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 108*x^66 + 101*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 119*x^25 + 44*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 20*x^18 + 111*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 113*x^9 + 4*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 60*x^2 + 33*x + 12, x^93 + 74*x^91 + 112*x^90 + 67*x^89 + 112*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 16*x^82 + 11*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 61*x^73 + 80*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 48*x^66 + 61*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 79*x^25 + 48*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 80*x^18 + 87*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 57*x^9 + 16*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 112*x^2 + 25*x + 112, x^93 + 74*x^91 + 116*x^90 + 75*x^89 + 68*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 60*x^82 + 3*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 85*x^73 + 108*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 20*x^66 + 37*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 119*x^25 + 20*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 108*x^18 + 47*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 113*x^9 + 60*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 68*x^2 + 97*x + 116, x^93 + 74*x^91 + 120*x^90 + 83*x^89 + 40*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 104*x^82 + 59*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 109*x^73 + 56*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 120*x^66 + 77*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 31*x^25 + 72*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 8*x^18 + 71*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 41*x^9 + 88*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 24*x^2 + 105*x + 72, x^93 + 74*x^91 + 92*x^90 + 43*x^89 + 108*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 52*x^82 + 35*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 117*x^73 + 36*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 60*x^66 + 5*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 87*x^25 + 92*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 68*x^18 + 79*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 17*x^9 + 20*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 76*x^2 + 65*x + 124, x^93 + 74*x^91 + 12*x^90 + 59*x^89 + 108*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 4*x^82 + 83*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 37*x^73 + 36*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 44*x^66 + 21*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 39*x^25 + 92*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 84*x^18 + 63*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + x^9 + 20*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 124*x^2 + 17*x + 60, x^93 + 74*x^91 + 24*x^90 + 35*x^89 + 24*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 72*x^82 + 107*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 93*x^73 + 8*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 24*x^66 + 93*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 47*x^25 + 120*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 104*x^18 + 55*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 89*x^9 + 104*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 56*x^2 + 57*x + 120, x^93 + 74*x^91 + 68*x^90 + 11*x^89 + 20*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 44*x^82 + 67*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 21*x^73 + 92*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 100*x^66 + 101*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 55*x^25 + 36*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 28*x^18 + 111*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 49*x^9 + 108*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 84*x^2 + 33*x + 4, x^93 + 74*x^91 + 16*x^90 + 19*x^89 + 32*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 38*x^83 + 112*x^82 + 59*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 45*x^73 + 96*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 50*x^67 + 80*x^66 + 77*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 95*x^25 + 32*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 94*x^19 + 48*x^18 + 71*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 105*x^9 + 96*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 42*x^3 + 16*x^2 + 105*x + 96, x^93 + 74*x^91 + 19*x^89 + 80*x^88 + 68*x^87 + 33*x^85 + 96*x^84 + 102*x^83 + 123*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 45*x^73 + 112*x^72 + 116*x^71 + 39*x^69 + 96*x^68 + 114*x^67 + 13*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 95*x^25 + 16*x^24 + 116*x^23 + 69*x^21 + 96*x^20 + 30*x^19 + 7*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 105*x^9 + 48*x^8 + 68*x^7 + 59*x^5 + 96*x^4 + 106*x^3 + 41*x + 16, x^93 + 74*x^91 + 4*x^90 + 27*x^89 + 36*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 108*x^82 + 51*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 69*x^73 + 12*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 36*x^66 + 53*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 7*x^25 + 116*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 92*x^18 + 31*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 33*x^9 + 92*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 20*x^2 + 49*x + 84, x^93 + 74*x^91 + 124*x^90 + 123*x^89 + 60*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 84*x^82 + 19*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 101*x^73 + 20*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 28*x^66 + 85*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 103*x^25 + 108*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 100*x^18 + 127*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 65*x^9 + 68*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 44*x^2 + 81*x + 76, x^93 + 74*x^91 + 44*x^90 + 59*x^89 + 12*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 100*x^82 + 83*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 37*x^73 + 4*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 76*x^66 + 21*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 39*x^25 + 124*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 52*x^18 + 63*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + x^9 + 116*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 28*x^2 + 17*x + 92, x^93 + 74*x^91 + 88*x^90 + 35*x^89 + 88*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 8*x^82 + 107*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 93*x^73 + 72*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 88*x^66 + 93*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 47*x^25 + 56*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 40*x^18 + 55*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 89*x^9 + 40*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 120*x^2 + 57*x + 56, x^93 + 74*x^91 + 48*x^90 + 19*x^89 + 64*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 102*x^83 + 16*x^82 + 123*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 45*x^73 + 64*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 114*x^67 + 48*x^66 + 13*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 95*x^25 + 64*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 30*x^19 + 80*x^18 + 7*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 105*x^9 + 64*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 106*x^3 + 112*x^2 + 41*x + 64, x^93 + 74*x^91 + 20*x^90 + 11*x^89 + 36*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 92*x^82 + 3*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 21*x^73 + 12*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 116*x^66 + 37*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 55*x^25 + 116*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 12*x^18 + 47*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 49*x^9 + 92*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 36*x^2 + 97*x + 20, x^93 + 74*x^91 + 96*x^90 + 67*x^89 + 32*x^88 + 68*x^87 + 65*x^85 + 102*x^83 + 96*x^82 + 11*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 61*x^73 + 96*x^72 + 116*x^71 + 71*x^69 + 114*x^67 + 32*x^66 + 61*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 79*x^25 + 32*x^24 + 116*x^23 + 101*x^21 + 30*x^19 + 96*x^18 + 87*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 57*x^9 + 96*x^8 + 68*x^7 + 91*x^5 + 106*x^3 + 32*x^2 + 25*x + 96, x^93 + 74*x^91 + 28*x^90 + 75*x^89 + 44*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 116*x^82 + 3*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 85*x^73 + 100*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 124*x^66 + 37*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 119*x^25 + 28*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 4*x^18 + 47*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 113*x^9 + 84*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 12*x^2 + 97*x + 60, x^93 + 74*x^91 + 40*x^90 + 83*x^89 + 56*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 56*x^82 + 123*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 109*x^73 + 104*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 104*x^66 + 13*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 31*x^25 + 24*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 24*x^18 + 7*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 41*x^9 + 72*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 72*x^2 + 41*x + 88, x^93 + 74*x^91 + 88*x^90 + 19*x^89 + 8*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 8*x^82 + 123*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 45*x^73 + 88*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 88*x^66 + 13*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 95*x^25 + 40*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 40*x^18 + 7*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 105*x^9 + 120*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 120*x^2 + 41*x + 40, x^93 + 74*x^91 + 28*x^90 + 91*x^89 + 60*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 116*x^82 + 115*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 5*x^73 + 20*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 124*x^66 + 117*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 71*x^25 + 108*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 4*x^18 + 95*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 97*x^9 + 68*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 12*x^2 + 113*x + 12, x^93 + 74*x^91 + 124*x^90 + 11*x^89 + 108*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 20*x^82 + 67*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 21*x^73 + 36*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 92*x^66 + 101*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 55*x^25 + 92*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 36*x^18 + 111*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 49*x^9 + 20*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 108*x^2 + 33*x + 124, x^93 + 74*x^91 + 80*x^90 + 51*x^89 + 64*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 102*x^83 + 112*x^82 + 91*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 13*x^73 + 64*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 114*x^67 + 80*x^66 + 45*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 127*x^25 + 64*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 30*x^19 + 48*x^18 + 103*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 73*x^9 + 64*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 106*x^3 + 16*x^2 + 73*x + 64, x^93 + 74*x^91 + 56*x^90 + 19*x^89 + 104*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 104*x^82 + 59*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 45*x^73 + 120*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 120*x^66 + 77*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 95*x^25 + 8*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 8*x^18 + 71*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 105*x^9 + 24*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 24*x^2 + 105*x + 72, x^93 + 74*x^91 + 52*x^90 + 59*x^89 + 84*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 124*x^82 + 19*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 37*x^73 + 28*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 84*x^66 + 85*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 39*x^25 + 100*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 44*x^18 + 127*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + x^9 + 44*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 4*x^2 + 81*x + 68, x^93 + 74*x^91 + 72*x^90 + 51*x^89 + 24*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 24*x^82 + 27*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 13*x^73 + 8*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 8*x^66 + 109*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 127*x^25 + 120*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 120*x^18 + 39*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 73*x^9 + 104*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 104*x^2 + 9*x + 56, x^93 + 74*x^91 + 20*x^90 + 91*x^89 + 20*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 28*x^82 + 115*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 5*x^73 + 92*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 52*x^66 + 117*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 71*x^25 + 36*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 76*x^18 + 95*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 97*x^9 + 108*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 100*x^2 + 113*x + 4, x^93 + 74*x^91 + 36*x^90 + 107*x^89 + 116*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 12*x^82 + 35*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 53*x^73 + 124*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 4*x^66 + 5*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 23*x^25 + 4*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 124*x^18 + 79*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 81*x^9 + 12*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 116*x^2 + 65*x + 36, x^93 + 74*x^91 + 52*x^90 + 11*x^89 + 4*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 60*x^82 + 3*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 21*x^73 + 44*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 20*x^66 + 37*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 55*x^25 + 84*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 108*x^18 + 47*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 49*x^9 + 124*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 68*x^2 + 97*x + 116, x^93 + 74*x^91 + 108*x^90 + 107*x^89 + 60*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 100*x^82 + 99*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 53*x^73 + 20*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 76*x^66 + 69*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 23*x^25 + 108*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 52*x^18 + 15*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 81*x^9 + 68*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 28*x^2 + x + 12, x^93 + 74*x^91 + 16*x^90 + 3*x^89 + 80*x^88 + 4*x^87 + 96*x^86 + x^85 + 96*x^84 + 38*x^83 + 48*x^82 + 11*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 125*x^73 + 112*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 16*x^66 + 61*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 15*x^25 + 16*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 112*x^18 + 87*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 121*x^9 + 48*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 80*x^2 + 25*x + 16, x^93 + 74*x^91 + 76*x^90 + 11*x^89 + 92*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 4*x^82 + 67*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 21*x^73 + 116*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 44*x^66 + 101*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 55*x^25 + 12*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 84*x^18 + 111*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 49*x^9 + 36*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 124*x^2 + 33*x + 44, x^93 + 74*x^91 + 104*x^90 + 35*x^89 + 40*x^88 + 68*x^87 + 112*x^86 + x^85 + 48*x^84 + 102*x^83 + 120*x^82 + 43*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 93*x^73 + 56*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 40*x^66 + 29*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 47*x^25 + 72*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 88*x^18 + 119*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 89*x^9 + 88*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 8*x^2 + 121*x + 8, x^93 + 74*x^91 + 100*x^90 + 27*x^89 + 36*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 12*x^82 + 51*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 69*x^73 + 12*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 4*x^66 + 53*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 7*x^25 + 116*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 124*x^18 + 31*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 33*x^9 + 92*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 116*x^2 + 49*x + 84, x^93 + 74*x^91 + 99*x^89 + 96*x^88 + 68*x^87 + 64*x^86 + x^85 + 102*x^83 + 64*x^82 + 107*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 29*x^73 + 32*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 114*x^67 + 64*x^66 + 93*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 111*x^25 + 96*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 30*x^19 + 64*x^18 + 55*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 25*x^9 + 32*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 106*x^3 + 64*x^2 + 57*x + 32, x^93 + 74*x^91 + 76*x^90 + 123*x^89 + 44*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 4*x^82 + 83*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 101*x^73 + 100*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 44*x^66 + 21*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 103*x^25 + 28*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 84*x^18 + 63*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 65*x^9 + 84*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 124*x^2 + 17*x + 60, x^93 + 74*x^91 + 52*x^90 + 91*x^89 + 116*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 124*x^82 + 115*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 5*x^73 + 124*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 84*x^66 + 117*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 71*x^25 + 4*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 44*x^18 + 95*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 97*x^9 + 12*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 4*x^2 + 113*x + 100, x^93 + 74*x^91 + 64*x^90 + 115*x^89 + 16*x^88 + 68*x^87 + 97*x^85 + 96*x^84 + 102*x^83 + 64*x^82 + 27*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 77*x^73 + 48*x^72 + 116*x^71 + 103*x^69 + 96*x^68 + 114*x^67 + 64*x^66 + 109*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 63*x^25 + 80*x^24 + 116*x^23 + 5*x^21 + 96*x^20 + 30*x^19 + 64*x^18 + 39*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 9*x^9 + 112*x^8 + 68*x^7 + 123*x^5 + 96*x^4 + 106*x^3 + 64*x^2 + 9*x + 80, x^93 + 74*x^91 + 32*x^90 + 115*x^89 + 16*x^88 + 4*x^87 + 33*x^85 + 32*x^84 + 38*x^83 + 32*x^82 + 91*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 77*x^73 + 48*x^72 + 52*x^71 + 39*x^69 + 32*x^68 + 50*x^67 + 96*x^66 + 45*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 63*x^25 + 80*x^24 + 52*x^23 + 69*x^21 + 32*x^20 + 94*x^19 + 32*x^18 + 103*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 9*x^9 + 112*x^8 + 4*x^7 + 59*x^5 + 32*x^4 + 42*x^3 + 96*x^2 + 73*x + 16, x^93 + 74*x^91 + 72*x^90 + 51*x^89 + 24*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 88*x^82 + 91*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 13*x^73 + 8*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 72*x^66 + 45*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 127*x^25 + 120*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 56*x^18 + 103*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 73*x^9 + 104*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 40*x^2 + 73*x + 120, x^93 + 74*x^91 + 80*x^90 + 51*x^89 + 64*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 48*x^82 + 27*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 13*x^73 + 64*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 16*x^66 + 109*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 127*x^25 + 64*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 112*x^18 + 39*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 73*x^9 + 64*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 80*x^2 + 9*x, x^93 + 74*x^91 + 100*x^90 + 43*x^89 + 84*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 12*x^82 + 35*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 117*x^73 + 28*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 4*x^66 + 5*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 87*x^25 + 100*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 124*x^18 + 79*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 17*x^9 + 44*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 116*x^2 + 65*x + 68, x^93 + 74*x^91 + 120*x^90 + 3*x^89 + 56*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 40*x^82 + 75*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 125*x^73 + 104*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 56*x^66 + 125*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 15*x^25 + 24*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 72*x^18 + 23*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 121*x^9 + 72*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 88*x^2 + 89*x + 88, x^93 + 74*x^91 + 64*x^90 + 3*x^89 + 64*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 102*x^83 + 75*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 125*x^73 + 64*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 114*x^67 + 125*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 15*x^25 + 64*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 30*x^19 + 23*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 121*x^9 + 64*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 106*x^3 + 89*x, x^93 + 74*x^91 + 8*x^90 + 115*x^89 + 120*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 24*x^82 + 27*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 77*x^73 + 40*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 8*x^66 + 109*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 63*x^25 + 88*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 120*x^18 + 39*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 9*x^9 + 8*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 104*x^2 + 9*x + 88, x^93 + 74*x^91 + 92*x^90 + 59*x^89 + 124*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 52*x^82 + 19*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 37*x^73 + 84*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 60*x^66 + 85*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 39*x^25 + 44*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 68*x^18 + 127*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + x^9 + 4*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 76*x^2 + 81*x + 76, x^93 + 74*x^91 + 112*x^90 + 51*x^89 + 32*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 38*x^83 + 16*x^82 + 27*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 13*x^73 + 96*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 50*x^67 + 48*x^66 + 109*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 127*x^25 + 32*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 94*x^19 + 80*x^18 + 39*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 73*x^9 + 96*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 42*x^3 + 112*x^2 + 9*x + 96, x^93 + 74*x^91 + 32*x^90 + 19*x^89 + 80*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 102*x^83 + 96*x^82 + 123*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 45*x^73 + 112*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 114*x^67 + 32*x^66 + 13*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 95*x^25 + 16*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 30*x^19 + 96*x^18 + 7*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 105*x^9 + 48*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 106*x^3 + 32*x^2 + 41*x + 16, x^93 + 74*x^91 + 72*x^90 + 67*x^89 + 104*x^88 + 4*x^87 + 112*x^86 + x^85 + 112*x^84 + 38*x^83 + 88*x^82 + 75*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 61*x^73 + 120*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 72*x^66 + 125*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 79*x^25 + 8*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 56*x^18 + 23*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 57*x^9 + 24*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 40*x^2 + 89*x + 8, x^93 + 74*x^91 + 40*x^90 + 67*x^89 + 104*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 56*x^82 + 11*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 61*x^73 + 120*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 104*x^66 + 61*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 79*x^25 + 8*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 24*x^18 + 87*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 57*x^9 + 24*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 72*x^2 + 25*x + 72, x^93 + 74*x^91 + 16*x^90 + 67*x^89 + 48*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 112*x^82 + 11*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 61*x^73 + 16*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 80*x^66 + 61*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 79*x^25 + 112*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 48*x^18 + 87*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 57*x^9 + 80*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 16*x^2 + 25*x + 48, x^93 + 74*x^91 + 3*x^89 + 64*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 102*x^83 + 64*x^82 + 75*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 125*x^73 + 64*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 114*x^67 + 64*x^66 + 125*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 15*x^25 + 64*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 30*x^19 + 64*x^18 + 23*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 121*x^9 + 64*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 106*x^3 + 64*x^2 + 89*x, x^93 + 74*x^91 + 76*x^90 + 123*x^89 + 44*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 68*x^82 + 19*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 101*x^73 + 100*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 108*x^66 + 85*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 103*x^25 + 28*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 20*x^18 + 127*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 65*x^9 + 84*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 60*x^2 + 81*x + 124, x^93 + 74*x^91 + 124*x^90 + 11*x^89 + 44*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 84*x^82 + 3*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 21*x^73 + 100*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 28*x^66 + 37*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 55*x^25 + 28*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 100*x^18 + 47*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 49*x^9 + 84*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 44*x^2 + 97*x + 124, x^93 + 74*x^91 + 124*x^90 + 107*x^89 + 44*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 20*x^82 + 99*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 53*x^73 + 100*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 92*x^66 + 69*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 23*x^25 + 28*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 36*x^18 + 15*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 81*x^9 + 84*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 108*x^2 + x + 60, x^93 + 74*x^91 + 8*x^90 + 99*x^89 + 40*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 24*x^82 + 43*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 29*x^73 + 56*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 8*x^66 + 29*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 111*x^25 + 72*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 120*x^18 + 119*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 25*x^9 + 88*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 104*x^2 + 121*x + 72, x^93 + 74*x^91 + 104*x^90 + 51*x^89 + 88*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 120*x^82 + 27*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 13*x^73 + 72*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 40*x^66 + 109*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 127*x^25 + 56*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 88*x^18 + 39*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 73*x^9 + 40*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 8*x^2 + 9*x + 120, x^93 + 74*x^91 + 20*x^90 + 27*x^89 + 52*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 92*x^82 + 115*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 69*x^73 + 60*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 116*x^66 + 117*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 7*x^25 + 68*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 12*x^18 + 95*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 33*x^9 + 76*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 36*x^2 + 113*x + 100, x^93 + 74*x^91 + 76*x^90 + 107*x^89 + 60*x^88 + 100*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 6*x^83 + 68*x^82 + 35*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 53*x^73 + 20*x^72 + 20*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 18*x^67 + 108*x^66 + 5*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 23*x^25 + 108*x^24 + 20*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 62*x^19 + 20*x^18 + 79*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 81*x^9 + 68*x^8 + 100*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 10*x^3 + 60*x^2 + 65*x + 76, x^93 + 74*x^91 + 24*x^90 + 35*x^89 + 88*x^88 + 68*x^87 + 16*x^86 + x^85 + 80*x^84 + 102*x^83 + 8*x^82 + 43*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 93*x^73 + 72*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 88*x^66 + 29*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 47*x^25 + 56*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 40*x^18 + 119*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 89*x^9 + 40*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 120*x^2 + 121*x + 120, x^93 + 74*x^91 + 20*x^90 + 107*x^89 + 68*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 28*x^82 + 99*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 53*x^73 + 108*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 52*x^66 + 69*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 23*x^25 + 20*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 76*x^18 + 15*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 81*x^9 + 60*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 100*x^2 + x + 116, x^93 + 74*x^91 + 124*x^90 + 123*x^89 + 124*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 20*x^82 + 83*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 101*x^73 + 84*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 92*x^66 + 21*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 103*x^25 + 44*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 36*x^18 + 63*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 65*x^9 + 4*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 108*x^2 + 17*x + 76, x^93 + 74*x^91 + 56*x^90 + 83*x^89 + 40*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 40*x^82 + 59*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 109*x^73 + 56*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 56*x^66 + 77*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 31*x^25 + 72*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 72*x^18 + 71*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 41*x^9 + 88*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 88*x^2 + 105*x + 72, x^93 + 74*x^91 + 92*x^90 + 107*x^89 + 108*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 116*x^82 + 35*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 53*x^73 + 36*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 124*x^66 + 5*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 23*x^25 + 92*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 4*x^18 + 79*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 81*x^9 + 20*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 12*x^2 + 65*x + 60, x^93 + 74*x^91 + 32*x^90 + 67*x^89 + 96*x^88 + 68*x^87 + 65*x^85 + 102*x^83 + 32*x^82 + 11*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 61*x^73 + 32*x^72 + 116*x^71 + 71*x^69 + 114*x^67 + 96*x^66 + 61*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 79*x^25 + 96*x^24 + 116*x^23 + 101*x^21 + 30*x^19 + 32*x^18 + 87*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 57*x^9 + 32*x^8 + 68*x^7 + 91*x^5 + 106*x^3 + 96*x^2 + 25*x + 32, x^93 + 74*x^91 + 116*x^90 + 91*x^89 + 116*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 124*x^82 + 51*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 5*x^73 + 124*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 84*x^66 + 53*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 71*x^25 + 4*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 44*x^18 + 31*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 97*x^9 + 12*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 4*x^2 + 49*x + 36, x^93 + 74*x^91 + 64*x^90 + 115*x^89 + 80*x^88 + 68*x^87 + 97*x^85 + 96*x^84 + 102*x^83 + 64*x^82 + 27*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 77*x^73 + 112*x^72 + 116*x^71 + 103*x^69 + 96*x^68 + 114*x^67 + 64*x^66 + 109*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 63*x^25 + 16*x^24 + 116*x^23 + 5*x^21 + 96*x^20 + 30*x^19 + 64*x^18 + 39*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 9*x^9 + 48*x^8 + 68*x^7 + 123*x^5 + 96*x^4 + 106*x^3 + 64*x^2 + 9*x + 16, x^93 + 74*x^91 + 12*x^90 + 27*x^89 + 12*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 68*x^82 + 51*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 69*x^73 + 4*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 108*x^66 + 53*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 7*x^25 + 124*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 20*x^18 + 31*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 33*x^9 + 116*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 60*x^2 + 49*x + 28, x^93 + 74*x^91 + 104*x^90 + 3*x^89 + 8*x^88 + 4*x^87 + 48*x^86 + x^85 + 48*x^84 + 38*x^83 + 56*x^82 + 11*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 125*x^73 + 88*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 104*x^66 + 61*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 15*x^25 + 40*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 24*x^18 + 87*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 121*x^9 + 120*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 72*x^2 + 25*x + 40, x^93 + 74*x^91 + 72*x^90 + 115*x^89 + 56*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 88*x^82 + 27*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 77*x^73 + 104*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 72*x^66 + 109*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 63*x^25 + 24*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 56*x^18 + 39*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 9*x^9 + 72*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 40*x^2 + 9*x + 24, x^93 + 74*x^91 + 116*x^90 + 11*x^89 + 100*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 124*x^82 + 3*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 21*x^73 + 76*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 84*x^66 + 37*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 55*x^25 + 52*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 44*x^18 + 47*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 49*x^9 + 28*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 4*x^2 + 97*x + 84, x^93 + 74*x^91 + 100*x^90 + 107*x^89 + 20*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 12*x^82 + 99*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 53*x^73 + 92*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 4*x^66 + 69*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 23*x^25 + 36*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 124*x^18 + 15*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 81*x^9 + 108*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 116*x^2 + x + 4, x^93 + 74*x^91 + 48*x^90 + 83*x^89 + 32*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 38*x^83 + 80*x^82 + 123*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 109*x^73 + 96*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 50*x^67 + 112*x^66 + 13*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 31*x^25 + 32*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 94*x^19 + 16*x^18 + 7*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 41*x^9 + 96*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 42*x^3 + 48*x^2 + 41*x + 96, x^93 + 74*x^91 + 116*x^90 + 107*x^89 + 68*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 124*x^82 + 35*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 53*x^73 + 108*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 84*x^66 + 5*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 23*x^25 + 20*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 44*x^18 + 79*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 81*x^9 + 60*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 4*x^2 + 65*x + 52, x^93 + 74*x^91 + 4*x^90 + 107*x^89 + 116*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 108*x^82 + 99*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 53*x^73 + 124*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 36*x^66 + 69*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 23*x^25 + 4*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 92*x^18 + 15*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 81*x^9 + 12*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 20*x^2 + x + 100, x^93 + 74*x^91 + 68*x^90 + 59*x^89 + 100*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 44*x^82 + 19*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 37*x^73 + 76*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 100*x^66 + 85*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 39*x^25 + 52*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 28*x^18 + 127*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + x^9 + 28*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 84*x^2 + 81*x + 20, x^93 + 74*x^91 + 4*x^90 + 59*x^89 + 68*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 108*x^82 + 19*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 37*x^73 + 108*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 36*x^66 + 85*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 39*x^25 + 20*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 92*x^18 + 127*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + x^9 + 60*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 20*x^2 + 81*x + 116, x^93 + 74*x^91 + 28*x^90 + 59*x^89 + 60*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 52*x^82 + 83*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 37*x^73 + 20*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 60*x^66 + 21*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 39*x^25 + 108*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 68*x^18 + 63*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + x^9 + 68*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 76*x^2 + 17*x + 76, x^93 + 74*x^91 + 12*x^90 + 123*x^89 + 12*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 4*x^82 + 19*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 101*x^73 + 4*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 44*x^66 + 85*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 103*x^25 + 124*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 84*x^18 + 127*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 65*x^9 + 116*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 124*x^2 + 81*x + 92, x^93 + 74*x^91 + 4*x^90 + 27*x^89 + 36*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 44*x^82 + 115*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 69*x^73 + 12*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 100*x^66 + 117*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 7*x^25 + 116*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 28*x^18 + 95*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 33*x^9 + 92*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 84*x^2 + 113*x + 20, x^93 + 74*x^91 + 24*x^90 + 115*x^89 + 104*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 72*x^82 + 27*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 77*x^73 + 120*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 24*x^66 + 109*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 63*x^25 + 8*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 104*x^18 + 39*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 9*x^9 + 24*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 56*x^2 + 9*x + 8, x^93 + 74*x^91 + 72*x^90 + 83*x^89 + 56*x^88 + 4*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 24*x^82 + 123*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 109*x^73 + 104*x^72 + 52*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 8*x^66 + 13*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 31*x^25 + 24*x^24 + 52*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 120*x^18 + 7*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 41*x^9 + 72*x^8 + 4*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 104*x^2 + 41*x + 88, x^93 + 74*x^91 + 52*x^90 + 43*x^89 + 4*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 124*x^82 + 35*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 117*x^73 + 44*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 84*x^66 + 5*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 87*x^25 + 84*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 44*x^18 + 79*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 17*x^9 + 124*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 4*x^2 + 65*x + 52, x^93 + 74*x^91 + 8*x^90 + 51*x^89 + 24*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 88*x^82 + 27*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 13*x^73 + 8*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 72*x^66 + 109*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 127*x^25 + 120*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 56*x^18 + 39*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 73*x^9 + 104*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 40*x^2 + 9*x + 56, x^93 + 74*x^91 + 4*x^90 + 43*x^89 + 116*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 108*x^82 + 35*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 117*x^73 + 124*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 36*x^66 + 5*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 87*x^25 + 4*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 92*x^18 + 79*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 17*x^9 + 12*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 20*x^2 + 65*x + 100, x^93 + 74*x^91 + 28*x^90 + 91*x^89 + 92*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 52*x^82 + 51*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 5*x^73 + 116*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 60*x^66 + 53*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 71*x^25 + 12*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 68*x^18 + 31*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 97*x^9 + 36*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 76*x^2 + 49*x + 108, x^93 + 74*x^91 + 88*x^90 + 51*x^89 + 72*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 8*x^82 + 91*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 13*x^73 + 24*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 88*x^66 + 45*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 127*x^25 + 104*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 40*x^18 + 103*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 73*x^9 + 56*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 120*x^2 + 73*x + 104, x^93 + 74*x^91 + 36*x^90 + 107*x^89 + 84*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 12*x^82 + 35*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 53*x^73 + 28*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 4*x^66 + 5*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 23*x^25 + 100*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 124*x^18 + 79*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 81*x^9 + 44*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 116*x^2 + 65*x + 4, x^93 + 74*x^91 + 4*x^90 + 123*x^89 + 36*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 44*x^82 + 19*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 101*x^73 + 12*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 100*x^66 + 85*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 103*x^25 + 116*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 28*x^18 + 127*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 65*x^9 + 92*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 84*x^2 + 81*x + 20, x^93 + 74*x^91 + 60*x^90 + 59*x^89 + 28*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 84*x^82 + 19*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 37*x^73 + 52*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 28*x^66 + 85*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 39*x^25 + 76*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 100*x^18 + 127*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + x^9 + 100*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 44*x^2 + 81*x + 108, x^93 + 74*x^91 + 32*x^90 + 115*x^89 + 112*x^88 + 4*x^87 + 33*x^85 + 96*x^84 + 38*x^83 + 32*x^82 + 91*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 77*x^73 + 80*x^72 + 52*x^71 + 39*x^69 + 96*x^68 + 50*x^67 + 96*x^66 + 45*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 63*x^25 + 48*x^24 + 52*x^23 + 69*x^21 + 96*x^20 + 94*x^19 + 32*x^18 + 103*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 9*x^9 + 16*x^8 + 4*x^7 + 59*x^5 + 96*x^4 + 42*x^3 + 96*x^2 + 73*x + 112, x^93 + 74*x^91 + 8*x^90 + 3*x^89 + 72*x^88 + 4*x^87 + 112*x^86 + x^85 + 48*x^84 + 38*x^83 + 24*x^82 + 11*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 125*x^73 + 24*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 8*x^66 + 61*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 15*x^25 + 104*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 120*x^18 + 87*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 121*x^9 + 56*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 104*x^2 + 25*x + 104, x^93 + 74*x^91 + 44*x^90 + 11*x^89 + 28*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 36*x^82 + 67*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 21*x^73 + 52*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 12*x^66 + 101*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 55*x^25 + 76*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 116*x^18 + 111*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 49*x^9 + 100*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 92*x^2 + 33*x + 108, x^93 + 74*x^91 + 92*x^90 + 107*x^89 + 76*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 116*x^82 + 35*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 53*x^73 + 68*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 124*x^66 + 5*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 23*x^25 + 60*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 4*x^18 + 79*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 81*x^9 + 52*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 12*x^2 + 65*x + 28, x^93 + 74*x^91 + 56*x^90 + 99*x^89 + 88*x^88 + 68*x^87 + 80*x^86 + x^85 + 80*x^84 + 102*x^83 + 104*x^82 + 107*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 29*x^73 + 72*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 120*x^66 + 93*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 111*x^25 + 56*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 8*x^18 + 55*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 25*x^9 + 40*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 24*x^2 + 57*x + 120, x^93 + 74*x^91 + 116*x^90 + 107*x^89 + 100*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 60*x^82 + 99*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 53*x^73 + 76*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 20*x^66 + 69*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 23*x^25 + 52*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 108*x^18 + 15*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 81*x^9 + 28*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 68*x^2 + x + 20, x^93 + 74*x^91 + 72*x^90 + 51*x^89 + 88*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 24*x^82 + 27*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 13*x^73 + 72*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 8*x^66 + 109*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 127*x^25 + 56*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 120*x^18 + 39*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 73*x^9 + 40*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 104*x^2 + 9*x + 120, x^93 + 74*x^91 + 116*x^90 + 27*x^89 + 52*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 60*x^82 + 51*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 69*x^73 + 60*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 20*x^66 + 53*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 7*x^25 + 68*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 108*x^18 + 31*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 33*x^9 + 76*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 68*x^2 + 49*x + 36, x^93 + 74*x^91 + 72*x^90 + 115*x^89 + 120*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 88*x^82 + 27*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 77*x^73 + 40*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 72*x^66 + 109*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 63*x^25 + 88*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 56*x^18 + 39*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 9*x^9 + 8*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 40*x^2 + 9*x + 88, x^93 + 74*x^91 + 116*x^90 + 75*x^89 + 100*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 60*x^82 + 3*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 85*x^73 + 76*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 20*x^66 + 37*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 119*x^25 + 52*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 108*x^18 + 47*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 113*x^9 + 28*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 68*x^2 + 97*x + 20, x^93 + 74*x^91 + 28*x^90 + 43*x^89 + 76*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 116*x^82 + 35*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 117*x^73 + 68*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 124*x^66 + 5*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 87*x^25 + 60*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 4*x^18 + 79*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 17*x^9 + 52*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 12*x^2 + 65*x + 92, x^93 + 74*x^91 + 104*x^90 + 67*x^89 + 72*x^88 + 4*x^87 + 48*x^86 + x^85 + 48*x^84 + 38*x^83 + 56*x^82 + 75*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 61*x^73 + 24*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 104*x^66 + 125*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 79*x^25 + 104*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 24*x^18 + 23*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 57*x^9 + 56*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 72*x^2 + 89*x + 104, x^93 + 74*x^91 + 60*x^90 + 59*x^89 + 60*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 20*x^82 + 83*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 37*x^73 + 20*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 92*x^66 + 21*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 39*x^25 + 108*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 36*x^18 + 63*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + x^9 + 68*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 108*x^2 + 17*x + 76, x^93 + 74*x^91 + 64*x^90 + 99*x^89 + 96*x^88 + 4*x^87 + 65*x^85 + 64*x^84 + 38*x^83 + 64*x^82 + 43*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 29*x^73 + 32*x^72 + 52*x^71 + 71*x^69 + 64*x^68 + 50*x^67 + 64*x^66 + 29*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 111*x^25 + 96*x^24 + 52*x^23 + 101*x^21 + 64*x^20 + 94*x^19 + 64*x^18 + 119*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 25*x^9 + 32*x^8 + 4*x^7 + 91*x^5 + 64*x^4 + 42*x^3 + 64*x^2 + 121*x + 96, x^93 + 74*x^91 + 100*x^90 + 91*x^89 + 68*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 12*x^82 + 115*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 5*x^73 + 108*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 4*x^66 + 117*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 71*x^25 + 20*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 124*x^18 + 95*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 97*x^9 + 60*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 116*x^2 + 113*x + 116, x^93 + 74*x^91 + 52*x^90 + 75*x^89 + 36*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 60*x^82 + 67*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 85*x^73 + 12*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 20*x^66 + 101*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 119*x^25 + 116*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 108*x^18 + 111*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 113*x^9 + 92*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 68*x^2 + 33*x + 20, x^93 + 74*x^91 + 32*x^90 + 19*x^89 + 16*x^88 + 4*x^87 + 97*x^85 + 32*x^84 + 38*x^83 + 32*x^82 + 59*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 45*x^73 + 48*x^72 + 52*x^71 + 103*x^69 + 32*x^68 + 50*x^67 + 96*x^66 + 77*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 95*x^25 + 80*x^24 + 52*x^23 + 5*x^21 + 32*x^20 + 94*x^19 + 32*x^18 + 71*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 105*x^9 + 112*x^8 + 4*x^7 + 123*x^5 + 32*x^4 + 42*x^3 + 96*x^2 + 105*x + 16, x^93 + 74*x^91 + 4*x^90 + 75*x^89 + 116*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 44*x^82 + 67*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 85*x^73 + 124*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 100*x^66 + 101*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 119*x^25 + 4*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 28*x^18 + 111*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 113*x^9 + 12*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 84*x^2 + 33*x + 36, x^93 + 74*x^91 + 56*x^90 + 83*x^89 + 40*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 104*x^82 + 123*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 109*x^73 + 56*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 120*x^66 + 13*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 31*x^25 + 72*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 8*x^18 + 7*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 41*x^9 + 88*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 24*x^2 + 41*x + 8, x^93 + 74*x^91 + 24*x^90 + 51*x^89 + 72*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 72*x^82 + 91*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 13*x^73 + 24*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 24*x^66 + 45*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 127*x^25 + 104*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 104*x^18 + 103*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 73*x^9 + 56*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 56*x^2 + 73*x + 104, x^93 + 74*x^91 + 56*x^90 + 83*x^89 + 104*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 104*x^82 + 123*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 109*x^73 + 120*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 120*x^66 + 13*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 31*x^25 + 8*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 8*x^18 + 7*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 41*x^9 + 24*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 24*x^2 + 41*x + 72, x^93 + 74*x^91 + 28*x^90 + 123*x^89 + 92*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 52*x^82 + 19*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 101*x^73 + 116*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 60*x^66 + 85*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 103*x^25 + 12*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 68*x^18 + 127*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 65*x^9 + 36*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 76*x^2 + 81*x + 108, x^93 + 74*x^91 + 12*x^90 + 91*x^89 + 76*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 68*x^82 + 115*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 5*x^73 + 68*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 108*x^66 + 117*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 71*x^25 + 60*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 20*x^18 + 95*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 97*x^9 + 52*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 60*x^2 + 113*x + 92, x^93 + 74*x^91 + 48*x^90 + 51*x^89 + 96*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 38*x^83 + 80*x^82 + 27*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 13*x^73 + 32*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 50*x^67 + 112*x^66 + 109*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 127*x^25 + 96*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 94*x^19 + 16*x^18 + 39*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 73*x^9 + 32*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 42*x^3 + 48*x^2 + 9*x + 32, x^93 + 74*x^91 + 52*x^90 + 107*x^89 + 4*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 124*x^82 + 99*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 53*x^73 + 44*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 84*x^66 + 69*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 23*x^25 + 84*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 44*x^18 + 15*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 81*x^9 + 124*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 4*x^2 + x + 52, x^93 + 74*x^91 + 40*x^90 + 35*x^89 + 104*x^88 + 68*x^87 + 112*x^86 + x^85 + 48*x^84 + 102*x^83 + 56*x^82 + 43*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 93*x^73 + 120*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 104*x^66 + 29*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 47*x^25 + 8*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 24*x^18 + 119*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 89*x^9 + 24*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 72*x^2 + 121*x + 72, x^93 + 74*x^91 + 52*x^90 + 123*x^89 + 52*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 60*x^82 + 19*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 101*x^73 + 60*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 20*x^66 + 85*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 103*x^25 + 68*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 108*x^18 + 127*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 65*x^9 + 76*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 68*x^2 + 81*x + 100, x^93 + 74*x^91 + 36*x^90 + 107*x^89 + 52*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 76*x^82 + 99*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 53*x^73 + 60*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 68*x^66 + 69*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 23*x^25 + 68*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 60*x^18 + 15*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 81*x^9 + 76*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 52*x^2 + x + 36, x^93 + 74*x^91 + 40*x^90 + 99*x^89 + 40*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 120*x^82 + 43*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 29*x^73 + 56*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 40*x^66 + 29*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 111*x^25 + 72*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 88*x^18 + 119*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 25*x^9 + 88*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 8*x^2 + 121*x + 72, x^93 + 74*x^91 + 76*x^90 + 91*x^89 + 44*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 4*x^82 + 115*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 5*x^73 + 100*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 44*x^66 + 117*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 71*x^25 + 28*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 84*x^18 + 95*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 97*x^9 + 84*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 124*x^2 + 113*x + 60, x^93 + 74*x^91 + 40*x^90 + 115*x^89 + 24*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 120*x^82 + 27*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 77*x^73 + 8*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 40*x^66 + 109*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 63*x^25 + 120*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 88*x^18 + 39*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 9*x^9 + 104*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 8*x^2 + 9*x + 120, x^93 + 74*x^91 + 64*x^90 + 19*x^89 + 80*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 38*x^83 + 59*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 45*x^73 + 112*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 50*x^67 + 77*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 95*x^25 + 16*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 94*x^19 + 71*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 105*x^9 + 48*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 42*x^3 + 105*x + 80, x^93 + 74*x^91 + 12*x^90 + 43*x^89 + 124*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 68*x^82 + 35*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 117*x^73 + 84*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 108*x^66 + 5*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 87*x^25 + 44*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 20*x^18 + 79*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 17*x^9 + 4*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 60*x^2 + 65*x + 76, x^93 + 74*x^91 + 80*x^90 + 3*x^89 + 112*x^88 + 4*x^87 + 96*x^86 + x^85 + 32*x^84 + 38*x^83 + 112*x^82 + 11*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 125*x^73 + 80*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 80*x^66 + 61*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 15*x^25 + 48*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 48*x^18 + 87*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 121*x^9 + 16*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 16*x^2 + 25*x + 48, x^93 + 74*x^91 + 68*x^90 + 123*x^89 + 100*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 108*x^82 + 19*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 101*x^73 + 76*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 36*x^66 + 85*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 103*x^25 + 52*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 92*x^18 + 127*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 65*x^9 + 28*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 20*x^2 + 81*x + 84, x^93 + 74*x^91 + 96*x^90 + 19*x^89 + 112*x^88 + 4*x^87 + 97*x^85 + 96*x^84 + 38*x^83 + 96*x^82 + 59*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 45*x^73 + 80*x^72 + 52*x^71 + 103*x^69 + 96*x^68 + 50*x^67 + 32*x^66 + 77*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 95*x^25 + 48*x^24 + 52*x^23 + 5*x^21 + 96*x^20 + 94*x^19 + 96*x^18 + 71*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 105*x^9 + 16*x^8 + 4*x^7 + 123*x^5 + 96*x^4 + 42*x^3 + 32*x^2 + 105*x + 112, x^93 + 74*x^91 + 28*x^90 + 11*x^89 + 44*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 52*x^82 + 3*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 21*x^73 + 100*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 60*x^66 + 37*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 55*x^25 + 28*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 68*x^18 + 47*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 49*x^9 + 84*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 76*x^2 + 97*x + 124, x^93 + 74*x^91 + 12*x^90 + 59*x^89 + 108*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 68*x^82 + 19*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 37*x^73 + 36*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 108*x^66 + 85*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 39*x^25 + 92*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 20*x^18 + 127*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + x^9 + 20*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 60*x^2 + 81*x + 124, x^93 + 74*x^91 + 96*x^90 + 99*x^89 + 64*x^88 + 68*x^87 + x^85 + 64*x^84 + 102*x^83 + 96*x^82 + 107*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 29*x^73 + 64*x^72 + 116*x^71 + 7*x^69 + 64*x^68 + 114*x^67 + 32*x^66 + 93*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 111*x^25 + 64*x^24 + 116*x^23 + 37*x^21 + 64*x^20 + 30*x^19 + 96*x^18 + 55*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 25*x^9 + 64*x^8 + 68*x^7 + 27*x^5 + 64*x^4 + 106*x^3 + 32*x^2 + 57*x, x^93 + 74*x^91 + 28*x^90 + 59*x^89 + 92*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 52*x^82 + 83*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 37*x^73 + 116*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 60*x^66 + 21*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 39*x^25 + 12*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 68*x^18 + 63*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + x^9 + 36*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 76*x^2 + 17*x + 108, x^93 + 74*x^91 + 120*x^90 + 3*x^89 + 88*x^88 + 4*x^87 + 16*x^86 + x^85 + 16*x^84 + 38*x^83 + 104*x^82 + 11*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 125*x^73 + 72*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 120*x^66 + 61*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 15*x^25 + 56*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 8*x^18 + 87*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 121*x^9 + 40*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 24*x^2 + 25*x + 56, x^93 + 74*x^91 + 12*x^90 + 75*x^89 + 124*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 68*x^82 + 3*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 85*x^73 + 84*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 108*x^66 + 37*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 119*x^25 + 44*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 20*x^18 + 47*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 113*x^9 + 4*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 60*x^2 + 97*x + 76, x^93 + 74*x^91 + 80*x^90 + 3*x^89 + 16*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 48*x^82 + 75*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 125*x^73 + 48*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 16*x^66 + 125*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 15*x^25 + 80*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 112*x^18 + 23*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 121*x^9 + 112*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 80*x^2 + 89*x + 16, x^93 + 74*x^91 + 116*x^90 + 91*x^89 + 84*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 124*x^82 + 51*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 5*x^73 + 28*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 84*x^66 + 53*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 71*x^25 + 100*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 44*x^18 + 31*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 97*x^9 + 44*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 4*x^2 + 49*x + 4, x^93 + 74*x^91 + 80*x^90 + 83*x^89 + 96*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 38*x^83 + 48*x^82 + 123*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 109*x^73 + 32*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 50*x^67 + 16*x^66 + 13*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 31*x^25 + 96*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 94*x^19 + 112*x^18 + 7*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 41*x^9 + 32*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 42*x^3 + 80*x^2 + 41*x + 32, x^93 + 74*x^91 + 108*x^90 + 59*x^89 + 108*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 36*x^82 + 83*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 37*x^73 + 36*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 12*x^66 + 21*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 39*x^25 + 92*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 116*x^18 + 63*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + x^9 + 20*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 92*x^2 + 17*x + 60, x^93 + 74*x^91 + 83*x^89 + 16*x^88 + 68*x^87 + 33*x^85 + 96*x^84 + 102*x^83 + 59*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 109*x^73 + 48*x^72 + 116*x^71 + 39*x^69 + 96*x^68 + 114*x^67 + 77*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 31*x^25 + 80*x^24 + 116*x^23 + 69*x^21 + 96*x^20 + 30*x^19 + 71*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 41*x^9 + 112*x^8 + 68*x^7 + 59*x^5 + 96*x^4 + 106*x^3 + 105*x + 80, x^93 + 74*x^91 + 100*x^90 + 27*x^89 + 100*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 12*x^82 + 51*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 69*x^73 + 76*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 4*x^66 + 53*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 7*x^25 + 52*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 124*x^18 + 31*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 33*x^9 + 28*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 116*x^2 + 49*x + 20, x^93 + 74*x^91 + 108*x^90 + 11*x^89 + 92*x^88 + 100*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 36*x^82 + 3*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 21*x^73 + 116*x^72 + 20*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 12*x^66 + 37*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 55*x^25 + 12*x^24 + 20*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 116*x^18 + 47*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 49*x^9 + 36*x^8 + 100*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 92*x^2 + 97*x + 108, x^93 + 74*x^91 + 52*x^90 + 123*x^89 + 116*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 60*x^82 + 19*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 101*x^73 + 124*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 20*x^66 + 85*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 103*x^25 + 4*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 108*x^18 + 127*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 65*x^9 + 12*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 68*x^2 + 81*x + 36, x^93 + 74*x^91 + 96*x^90 + 19*x^89 + 112*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 32*x^84 + 102*x^83 + 32*x^82 + 123*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 45*x^73 + 80*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 32*x^68 + 114*x^67 + 96*x^66 + 13*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 95*x^25 + 48*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 32*x^20 + 30*x^19 + 32*x^18 + 7*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 105*x^9 + 16*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 32*x^4 + 106*x^3 + 96*x^2 + 41*x + 48, x^93 + 74*x^91 + 44*x^90 + 27*x^89 + 76*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 100*x^82 + 115*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 69*x^73 + 68*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 76*x^66 + 117*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 7*x^25 + 60*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 52*x^18 + 95*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 33*x^9 + 52*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 28*x^2 + 113*x + 28, x^93 + 74*x^91 + 36*x^90 + 11*x^89 + 84*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 76*x^82 + 67*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 21*x^73 + 28*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 68*x^66 + 101*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 55*x^25 + 100*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 60*x^18 + 111*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 49*x^9 + 44*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 52*x^2 + 33*x + 68, x^93 + 74*x^91 + 124*x^90 + 91*x^89 + 124*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 20*x^82 + 115*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 5*x^73 + 84*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 92*x^66 + 117*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 71*x^25 + 44*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 36*x^18 + 95*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 97*x^9 + 4*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 108*x^2 + 113*x + 76, x^93 + 74*x^91 + 64*x^90 + 51*x^89 + 80*x^88 + 68*x^87 + 97*x^85 + 96*x^84 + 102*x^83 + 64*x^82 + 91*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 13*x^73 + 112*x^72 + 116*x^71 + 103*x^69 + 96*x^68 + 114*x^67 + 64*x^66 + 45*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 127*x^25 + 16*x^24 + 116*x^23 + 5*x^21 + 96*x^20 + 30*x^19 + 64*x^18 + 103*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 73*x^9 + 48*x^8 + 68*x^7 + 123*x^5 + 96*x^4 + 106*x^3 + 64*x^2 + 73*x + 16, x^93 + 74*x^91 + 80*x^90 + 99*x^89 + 48*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 112*x^82 + 43*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 29*x^73 + 16*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 80*x^66 + 29*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 111*x^25 + 112*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 48*x^18 + 119*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 25*x^9 + 80*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 16*x^2 + 121*x + 112, x^93 + 74*x^91 + 116*x^90 + 27*x^89 + 116*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 60*x^82 + 51*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 69*x^73 + 124*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 20*x^66 + 53*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 7*x^25 + 4*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 108*x^18 + 31*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 33*x^9 + 12*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 68*x^2 + 49*x + 100, x^93 + 74*x^91 + 64*x^90 + 19*x^89 + 48*x^88 + 68*x^87 + 33*x^85 + 32*x^84 + 102*x^83 + 64*x^82 + 123*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 45*x^73 + 16*x^72 + 116*x^71 + 39*x^69 + 32*x^68 + 114*x^67 + 64*x^66 + 13*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 95*x^25 + 112*x^24 + 116*x^23 + 69*x^21 + 32*x^20 + 30*x^19 + 64*x^18 + 7*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 105*x^9 + 80*x^8 + 68*x^7 + 59*x^5 + 32*x^4 + 106*x^3 + 64*x^2 + 41*x + 112, x^93 + 74*x^91 + 60*x^90 + 27*x^89 + 92*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 20*x^82 + 115*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 69*x^73 + 116*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 92*x^66 + 117*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 7*x^25 + 12*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 36*x^18 + 95*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 33*x^9 + 36*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 108*x^2 + 113*x + 108, x^93 + 74*x^91 + 108*x^90 + 27*x^89 + 12*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 36*x^82 + 115*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 69*x^73 + 4*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 12*x^66 + 117*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 7*x^25 + 124*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 116*x^18 + 95*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 33*x^9 + 116*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 92*x^2 + 113*x + 92, x^93 + 74*x^91 + 88*x^90 + 83*x^89 + 40*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 8*x^82 + 59*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 109*x^73 + 56*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 88*x^66 + 77*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 31*x^25 + 72*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 40*x^18 + 71*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 41*x^9 + 88*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 120*x^2 + 105*x + 72, x^93 + 74*x^91 + 80*x^90 + 115*x^89 + 96*x^88 + 68*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 102*x^83 + 112*x^82 + 27*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 77*x^73 + 32*x^72 + 116*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 114*x^67 + 80*x^66 + 109*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 63*x^25 + 96*x^24 + 116*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 30*x^19 + 48*x^18 + 39*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 9*x^9 + 32*x^8 + 68*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 106*x^3 + 16*x^2 + 9*x + 96, x^93 + 74*x^91 + 60*x^90 + 43*x^89 + 12*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 84*x^82 + 35*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 117*x^73 + 4*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 28*x^66 + 5*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 87*x^25 + 124*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 100*x^18 + 79*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 17*x^9 + 116*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 44*x^2 + 65*x + 28, x^93 + 74*x^91 + 52*x^90 + 123*x^89 + 20*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 124*x^82 + 83*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 101*x^73 + 92*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 84*x^66 + 21*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 103*x^25 + 36*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 44*x^18 + 63*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 65*x^9 + 108*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 4*x^2 + 17*x + 4, x^93 + 74*x^91 + 52*x^90 + 59*x^89 + 84*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 60*x^82 + 83*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 37*x^73 + 28*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 20*x^66 + 21*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 39*x^25 + 100*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 108*x^18 + 63*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + x^9 + 44*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 68*x^2 + 17*x + 4, x^93 + 74*x^91 + 124*x^90 + 91*x^89 + 28*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 84*x^82 + 51*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 5*x^73 + 52*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 28*x^66 + 53*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 71*x^25 + 76*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 100*x^18 + 31*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 97*x^9 + 100*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 44*x^2 + 49*x + 44, x^93 + 74*x^91 + 20*x^90 + 91*x^89 + 84*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 92*x^82 + 51*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 5*x^73 + 28*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 116*x^66 + 53*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 71*x^25 + 100*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 12*x^18 + 31*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 97*x^9 + 44*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 36*x^2 + 49*x + 4, x^93 + 74*x^91 + 80*x^90 + 67*x^89 + 80*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 48*x^82 + 11*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 61*x^73 + 112*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 16*x^66 + 61*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 79*x^25 + 16*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 112*x^18 + 87*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 57*x^9 + 48*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 80*x^2 + 25*x + 80, x^93 + 74*x^91 + 88*x^90 + 3*x^89 + 88*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 72*x^82 + 75*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 125*x^73 + 72*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 24*x^66 + 125*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 15*x^25 + 56*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 104*x^18 + 23*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 121*x^9 + 40*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 56*x^2 + 89*x + 120, x^93 + 74*x^91 + 116*x^90 + 107*x^89 + 36*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 124*x^82 + 35*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 53*x^73 + 12*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 84*x^66 + 5*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 23*x^25 + 116*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 44*x^18 + 79*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 81*x^9 + 92*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 4*x^2 + 65*x + 20, x^93 + 74*x^91 + 104*x^90 + 115*x^89 + 88*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 56*x^82 + 27*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 77*x^73 + 72*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 104*x^66 + 109*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 63*x^25 + 56*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 24*x^18 + 39*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 9*x^9 + 40*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 72*x^2 + 9*x + 56, x^93 + 74*x^91 + 20*x^90 + 43*x^89 + 68*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 92*x^82 + 99*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 117*x^73 + 108*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 116*x^66 + 69*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 87*x^25 + 20*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 12*x^18 + 15*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 17*x^9 + 60*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 36*x^2 + x + 52, x^93 + 74*x^91 + 32*x^90 + 19*x^89 + 48*x^88 + 4*x^87 + 97*x^85 + 96*x^84 + 38*x^83 + 32*x^82 + 59*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 45*x^73 + 16*x^72 + 52*x^71 + 103*x^69 + 96*x^68 + 50*x^67 + 96*x^66 + 77*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 95*x^25 + 112*x^24 + 52*x^23 + 5*x^21 + 96*x^20 + 94*x^19 + 32*x^18 + 71*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 105*x^9 + 80*x^8 + 4*x^7 + 123*x^5 + 96*x^4 + 42*x^3 + 96*x^2 + 105*x + 48, x^93 + 74*x^91 + 104*x^90 + 3*x^89 + 72*x^88 + 4*x^87 + 48*x^86 + x^85 + 48*x^84 + 38*x^83 + 56*x^82 + 11*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 125*x^73 + 24*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 104*x^66 + 61*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 15*x^25 + 104*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 24*x^18 + 87*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 121*x^9 + 56*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 72*x^2 + 25*x + 104, x^93 + 74*x^91 + 88*x^90 + 19*x^89 + 40*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 72*x^82 + 59*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 45*x^73 + 56*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 24*x^66 + 77*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 95*x^25 + 72*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 104*x^18 + 71*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 105*x^9 + 88*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 56*x^2 + 105*x + 8, x^93 + 74*x^91 + 12*x^90 + 27*x^89 + 108*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 68*x^82 + 51*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 69*x^73 + 36*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 108*x^66 + 53*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 7*x^25 + 92*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 20*x^18 + 31*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 33*x^9 + 20*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 60*x^2 + 49*x + 124, x^93 + 74*x^91 + 16*x^90 + 99*x^89 + 112*x^88 + 68*x^87 + 32*x^86 + x^85 + 96*x^84 + 102*x^83 + 112*x^82 + 107*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 29*x^73 + 80*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 80*x^66 + 93*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 111*x^25 + 48*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 48*x^18 + 55*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 25*x^9 + 16*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 16*x^2 + 57*x + 112, x^93 + 74*x^91 + 88*x^90 + 19*x^89 + 104*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 72*x^82 + 59*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 45*x^73 + 120*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 24*x^66 + 77*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 95*x^25 + 8*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 104*x^18 + 71*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 105*x^9 + 24*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 56*x^2 + 105*x + 72, x^93 + 74*x^91 + 76*x^90 + 91*x^89 + 108*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 68*x^82 + 51*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 5*x^73 + 36*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 108*x^66 + 53*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 71*x^25 + 92*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 20*x^18 + 31*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 97*x^9 + 20*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 60*x^2 + 49*x + 60, x^93 + 74*x^91 + 124*x^90 + 11*x^89 + 76*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 20*x^82 + 67*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 21*x^73 + 68*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 92*x^66 + 101*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 55*x^25 + 60*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 36*x^18 + 111*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 49*x^9 + 52*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 108*x^2 + 33*x + 92, x^93 + 74*x^91 + 56*x^90 + 99*x^89 + 120*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 40*x^82 + 43*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 29*x^73 + 40*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 56*x^66 + 29*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 111*x^25 + 88*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 72*x^18 + 119*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 25*x^9 + 8*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 88*x^2 + 121*x + 88, x^93 + 74*x^91 + 16*x^90 + 19*x^89 + 64*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 112*x^82 + 59*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 45*x^73 + 64*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 80*x^66 + 77*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 95*x^25 + 64*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 48*x^18 + 71*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 105*x^9 + 64*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 16*x^2 + 105*x, x^93 + 74*x^91 + 92*x^90 + 123*x^89 + 124*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 116*x^82 + 19*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 101*x^73 + 84*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 124*x^66 + 85*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 103*x^25 + 44*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 4*x^18 + 127*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 65*x^9 + 4*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 12*x^2 + 81*x + 12, x^93 + 74*x^91 + 116*x^90 + 59*x^89 + 52*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 60*x^82 + 19*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 37*x^73 + 60*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 20*x^66 + 85*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 39*x^25 + 68*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 108*x^18 + 127*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + x^9 + 76*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 68*x^2 + 81*x + 36, x^93 + 74*x^91 + 40*x^90 + 51*x^89 + 56*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 56*x^82 + 27*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 13*x^73 + 104*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 104*x^66 + 109*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 127*x^25 + 24*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 24*x^18 + 39*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 73*x^9 + 72*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 72*x^2 + 9*x + 88, x^93 + 74*x^91 + 52*x^90 + 91*x^89 + 20*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 124*x^82 + 115*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 5*x^73 + 92*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 84*x^66 + 117*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 71*x^25 + 36*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 44*x^18 + 95*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 97*x^9 + 108*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 4*x^2 + 113*x + 4, x^93 + 74*x^91 + 36*x^90 + 91*x^89 + 4*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 76*x^82 + 115*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 5*x^73 + 44*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 68*x^66 + 117*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 71*x^25 + 84*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 60*x^18 + 95*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 97*x^9 + 124*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 52*x^2 + 113*x + 52, x^93 + 74*x^91 + 108*x^90 + 43*x^89 + 92*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 100*x^82 + 35*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 117*x^73 + 116*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 76*x^66 + 5*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 87*x^25 + 12*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 52*x^18 + 79*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 17*x^9 + 36*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 28*x^2 + 65*x + 44, x^93 + 74*x^91 + 40*x^90 + 67*x^89 + 104*x^88 + 4*x^87 + 48*x^86 + x^85 + 112*x^84 + 38*x^83 + 120*x^82 + 75*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 61*x^73 + 120*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 40*x^66 + 125*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 79*x^25 + 8*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 88*x^18 + 23*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 57*x^9 + 24*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 8*x^2 + 89*x + 8, x^93 + 74*x^91 + 104*x^90 + 83*x^89 + 88*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 120*x^82 + 123*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 109*x^73 + 72*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 40*x^66 + 13*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 31*x^25 + 56*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 88*x^18 + 7*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 41*x^9 + 40*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 8*x^2 + 41*x + 120, x^93 + 74*x^91 + 20*x^90 + 43*x^89 + 100*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 92*x^82 + 99*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 117*x^73 + 76*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 116*x^66 + 69*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 87*x^25 + 52*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 12*x^18 + 15*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 17*x^9 + 28*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 36*x^2 + x + 84, x^93 + 74*x^91 + 68*x^90 + 123*x^89 + 68*x^88 + 100*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 44*x^82 + 83*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 101*x^73 + 108*x^72 + 20*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 100*x^66 + 21*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 103*x^25 + 20*x^24 + 20*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 28*x^18 + 63*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 65*x^9 + 60*x^8 + 100*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 84*x^2 + 17*x + 116, x^93 + 74*x^91 + 92*x^90 + 91*x^89 + 60*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 52*x^82 + 115*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 5*x^73 + 20*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 60*x^66 + 117*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 71*x^25 + 108*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 68*x^18 + 95*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 97*x^9 + 68*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 76*x^2 + 113*x + 12, x^93 + 74*x^91 + 56*x^90 + 51*x^89 + 72*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 40*x^82 + 91*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 13*x^73 + 24*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 56*x^66 + 45*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 127*x^25 + 104*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 72*x^18 + 103*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 73*x^9 + 56*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 88*x^2 + 73*x + 104, x^93 + 74*x^91 + 96*x^90 + 99*x^89 + 68*x^87 + x^85 + 64*x^84 + 102*x^83 + 96*x^82 + 107*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 29*x^73 + 116*x^71 + 7*x^69 + 64*x^68 + 114*x^67 + 32*x^66 + 93*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 111*x^25 + 116*x^23 + 37*x^21 + 64*x^20 + 30*x^19 + 96*x^18 + 55*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 25*x^9 + 68*x^7 + 27*x^5 + 64*x^4 + 106*x^3 + 32*x^2 + 57*x + 64, x^93 + 74*x^91 + 80*x^90 + 99*x^89 + 112*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 112*x^82 + 43*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 29*x^73 + 80*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 80*x^66 + 29*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 111*x^25 + 48*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 48*x^18 + 119*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 25*x^9 + 16*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 16*x^2 + 121*x + 48, x^93 + 74*x^91 + 60*x^90 + 59*x^89 + 124*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 20*x^82 + 83*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 37*x^73 + 84*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 92*x^66 + 21*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 39*x^25 + 44*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 36*x^18 + 63*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + x^9 + 4*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 108*x^2 + 17*x + 12, x^93 + 74*x^91 + 92*x^90 + 11*x^89 + 108*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 52*x^82 + 67*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 21*x^73 + 36*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 60*x^66 + 101*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 55*x^25 + 92*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 68*x^18 + 111*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 49*x^9 + 20*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 76*x^2 + 33*x + 124, x^93 + 74*x^91 + 60*x^90 + 75*x^89 + 12*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 20*x^82 + 67*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 85*x^73 + 4*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 92*x^66 + 101*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 119*x^25 + 124*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 36*x^18 + 111*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 113*x^9 + 116*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 108*x^2 + 33*x + 92, x^93 + 74*x^91 + 80*x^90 + 83*x^89 + 32*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 38*x^83 + 48*x^82 + 123*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 109*x^73 + 96*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 50*x^67 + 16*x^66 + 13*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 31*x^25 + 32*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 94*x^19 + 112*x^18 + 7*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 41*x^9 + 96*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 42*x^3 + 80*x^2 + 41*x + 96, x^93 + 74*x^91 + 72*x^90 + 35*x^89 + 40*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 88*x^82 + 107*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 93*x^73 + 56*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 72*x^66 + 93*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 47*x^25 + 72*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 56*x^18 + 55*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 89*x^9 + 88*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 40*x^2 + 57*x + 72, x^93 + 74*x^91 + 24*x^90 + 83*x^89 + 8*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 72*x^82 + 59*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 109*x^73 + 88*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 24*x^66 + 77*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 31*x^25 + 40*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 104*x^18 + 71*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 41*x^9 + 120*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 56*x^2 + 105*x + 40, x^93 + 74*x^91 + 108*x^90 + 11*x^89 + 92*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 100*x^82 + 67*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 21*x^73 + 116*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 76*x^66 + 101*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 55*x^25 + 12*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 52*x^18 + 111*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 49*x^9 + 36*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 28*x^2 + 33*x + 44, x^93 + 74*x^91 + 36*x^90 + 75*x^89 + 52*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 12*x^82 + 67*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 85*x^73 + 60*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 4*x^66 + 101*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 119*x^25 + 68*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 124*x^18 + 111*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 113*x^9 + 76*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 116*x^2 + 33*x + 100, x^93 + 74*x^91 + 56*x^90 + 83*x^89 + 104*x^88 + 68*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 40*x^82 + 59*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 109*x^73 + 120*x^72 + 116*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 56*x^66 + 77*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 31*x^25 + 8*x^24 + 116*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 72*x^18 + 71*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 41*x^9 + 24*x^8 + 68*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 88*x^2 + 105*x + 8, x^93 + 74*x^91 + 60*x^90 + 43*x^89 + 12*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 20*x^82 + 99*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 117*x^73 + 4*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 92*x^66 + 69*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 87*x^25 + 124*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 36*x^18 + 15*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 17*x^9 + 116*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 108*x^2 + x + 92, x^93 + 74*x^91 + 72*x^90 + 115*x^89 + 24*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 88*x^82 + 27*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 77*x^73 + 8*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 72*x^66 + 109*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 63*x^25 + 120*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 56*x^18 + 39*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 9*x^9 + 104*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 40*x^2 + 9*x + 120, x^93 + 74*x^91 + 36*x^90 + 91*x^89 + 36*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 12*x^82 + 51*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 5*x^73 + 12*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 4*x^66 + 53*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 71*x^25 + 116*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 124*x^18 + 31*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 97*x^9 + 92*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 116*x^2 + 49*x + 20, x^93 + 74*x^91 + 4*x^90 + 43*x^89 + 84*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 44*x^82 + 99*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 117*x^73 + 28*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 100*x^66 + 69*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 87*x^25 + 100*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 28*x^18 + 15*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 17*x^9 + 44*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 84*x^2 + x + 4, x^93 + 74*x^91 + 56*x^90 + 35*x^89 + 88*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 40*x^82 + 107*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 93*x^73 + 72*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 56*x^66 + 93*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 47*x^25 + 56*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 72*x^18 + 55*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 89*x^9 + 40*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 88*x^2 + 57*x + 56, x^93 + 74*x^91 + 76*x^90 + 107*x^89 + 28*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 4*x^82 + 99*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 53*x^73 + 52*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 44*x^66 + 69*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 23*x^25 + 76*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 84*x^18 + 15*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 81*x^9 + 100*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 124*x^2 + x + 108, x^93 + 74*x^91 + 60*x^90 + 123*x^89 + 28*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 20*x^82 + 19*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 101*x^73 + 52*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 92*x^66 + 85*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 103*x^25 + 76*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 36*x^18 + 127*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 65*x^9 + 100*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 108*x^2 + 81*x + 44, x^93 + 74*x^91 + 112*x^90 + 67*x^89 + 48*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 16*x^82 + 11*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 61*x^73 + 16*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 48*x^66 + 61*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 79*x^25 + 112*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 80*x^18 + 87*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 57*x^9 + 80*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 112*x^2 + 25*x + 48, x^93 + 74*x^91 + 84*x^90 + 107*x^89 + 68*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 92*x^82 + 99*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 53*x^73 + 108*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 116*x^66 + 69*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 23*x^25 + 20*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 12*x^18 + 15*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 81*x^9 + 60*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 36*x^2 + x + 116, x^93 + 74*x^91 + 56*x^90 + 35*x^89 + 24*x^88 + 68*x^87 + 80*x^86 + x^85 + 80*x^84 + 102*x^83 + 104*x^82 + 43*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 93*x^73 + 8*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 120*x^66 + 29*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 47*x^25 + 120*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 8*x^18 + 119*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 89*x^9 + 104*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 24*x^2 + 121*x + 56, x^93 + 74*x^91 + 84*x^90 + 59*x^89 + 20*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 28*x^82 + 83*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 37*x^73 + 92*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 52*x^66 + 21*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 39*x^25 + 36*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 76*x^18 + 63*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + x^9 + 108*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 100*x^2 + 17*x + 68, x^93 + 74*x^91 + 16*x^90 + 19*x^89 + 4*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 112*x^82 + 59*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 45*x^73 + 52*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 80*x^66 + 77*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 95*x^25 + 52*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 48*x^18 + 71*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 105*x^9 + 4*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 16*x^2 + 105*x + 64, x^93 + 74*x^91 + 76*x^90 + 91*x^89 + 76*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 4*x^82 + 115*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 5*x^73 + 68*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 44*x^66 + 117*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 71*x^25 + 60*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 84*x^18 + 95*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 97*x^9 + 52*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 124*x^2 + 113*x + 92, x^93 + 74*x^91 + 8*x^90 + 3*x^89 + 8*x^88 + 4*x^87 + 112*x^86 + x^85 + 48*x^84 + 38*x^83 + 24*x^82 + 11*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 125*x^73 + 88*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 8*x^66 + 61*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 15*x^25 + 40*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 120*x^18 + 87*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 121*x^9 + 120*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 104*x^2 + 25*x + 40, x^93 + 74*x^91 + 108*x^90 + 123*x^89 + 44*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 100*x^82 + 83*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 101*x^73 + 100*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 76*x^66 + 21*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 103*x^25 + 28*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 52*x^18 + 63*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 65*x^9 + 84*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 28*x^2 + 17*x + 60, x^93 + 74*x^91 + 92*x^90 + 107*x^89 + 44*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 116*x^82 + 35*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 53*x^73 + 100*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 124*x^66 + 5*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 23*x^25 + 28*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 4*x^18 + 79*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 81*x^9 + 84*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 12*x^2 + 65*x + 124, x^93 + 74*x^91 + 60*x^90 + 43*x^89 + 76*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 84*x^82 + 35*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 117*x^73 + 68*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 28*x^66 + 5*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 87*x^25 + 60*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 100*x^18 + 79*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 17*x^9 + 52*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 44*x^2 + 65*x + 92, x^93 + 74*x^91 + 100*x^90 + 11*x^89 + 84*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 76*x^82 + 3*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 21*x^73 + 28*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 68*x^66 + 37*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 55*x^25 + 100*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 60*x^18 + 47*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 49*x^9 + 44*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 52*x^2 + 97*x + 4, x^93 + 74*x^91 + 72*x^90 + 35*x^89 + 72*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 88*x^82 + 107*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 93*x^73 + 24*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 72*x^66 + 93*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 47*x^25 + 104*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 56*x^18 + 55*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 89*x^9 + 56*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 40*x^2 + 57*x + 104, x^93 + 74*x^91 + 40*x^90 + 51*x^89 + 120*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 56*x^82 + 27*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 13*x^73 + 40*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 104*x^66 + 109*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 127*x^25 + 88*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 24*x^18 + 39*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 73*x^9 + 8*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 72*x^2 + 9*x + 24, x^93 + 74*x^91 + 76*x^90 + 11*x^89 + 124*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 4*x^82 + 67*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 21*x^73 + 84*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 44*x^66 + 101*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 55*x^25 + 44*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 84*x^18 + 111*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 49*x^9 + 4*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 124*x^2 + 33*x + 76, x^93 + 74*x^91 + 52*x^90 + 11*x^89 + 68*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 60*x^82 + 3*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 21*x^73 + 108*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 20*x^66 + 37*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 55*x^25 + 20*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 108*x^18 + 47*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 49*x^9 + 60*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 68*x^2 + 97*x + 52, x^93 + 74*x^91 + 8*x^90 + 115*x^89 + 24*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 24*x^82 + 27*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 77*x^73 + 8*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 8*x^66 + 109*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 63*x^25 + 120*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 120*x^18 + 39*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 9*x^9 + 104*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 104*x^2 + 9*x + 120, x^93 + 74*x^91 + 88*x^90 + 83*x^89 + 72*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 48*x^84 + 102*x^83 + 8*x^82 + 59*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 109*x^73 + 24*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 112*x^68 + 114*x^67 + 88*x^66 + 77*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 31*x^25 + 104*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 112*x^20 + 30*x^19 + 40*x^18 + 71*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 41*x^9 + 56*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 48*x^4 + 106*x^3 + 120*x^2 + 105*x + 104, x^93 + 74*x^91 + 112*x^90 + 83*x^89 + 32*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 80*x^82 + 59*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 109*x^73 + 96*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 112*x^66 + 77*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 31*x^25 + 32*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 16*x^18 + 71*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 41*x^9 + 96*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 48*x^2 + 105*x + 32, x^93 + 74*x^91 + 100*x^90 + 11*x^89 + 20*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 76*x^82 + 3*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 21*x^73 + 92*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 68*x^66 + 37*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 55*x^25 + 36*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 60*x^18 + 47*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 49*x^9 + 108*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 52*x^2 + 97*x + 68, x^93 + 74*x^91 + 16*x^90 + 83*x^89 + 64*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 102*x^83 + 48*x^82 + 59*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 109*x^73 + 64*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 114*x^67 + 16*x^66 + 77*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 31*x^25 + 64*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 30*x^19 + 112*x^18 + 71*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 41*x^9 + 64*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 106*x^3 + 80*x^2 + 105*x + 64, x^93 + 74*x^91 + 20*x^90 + 27*x^89 + 20*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 92*x^82 + 115*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 69*x^73 + 92*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 116*x^66 + 117*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 7*x^25 + 36*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 12*x^18 + 95*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 33*x^9 + 108*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 36*x^2 + 113*x + 68, x^93 + 74*x^91 + 36*x^90 + 91*x^89 + 4*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 12*x^82 + 51*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 5*x^73 + 44*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 4*x^66 + 53*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 71*x^25 + 84*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 124*x^18 + 31*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 97*x^9 + 124*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 116*x^2 + 49*x + 116, x^93 + 74*x^91 + 124*x^90 + 91*x^89 + 124*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 84*x^82 + 51*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 5*x^73 + 84*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 28*x^66 + 53*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 71*x^25 + 44*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 100*x^18 + 31*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 97*x^9 + 4*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 44*x^2 + 49*x + 12, x^93 + 74*x^91 + 16*x^90 + 83*x^89 + 32*x^88 + 68*x^87 + 96*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 48*x^82 + 59*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 109*x^73 + 96*x^72 + 116*x^71 + 96*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 16*x^66 + 77*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 31*x^25 + 32*x^24 + 116*x^23 + 96*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 112*x^18 + 71*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 41*x^9 + 96*x^8 + 68*x^7 + 96*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 80*x^2 + 105*x + 32, x^93 + 74*x^91 + 20*x^90 + 43*x^89 + 4*x^88 + 100*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 92*x^82 + 99*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 117*x^73 + 44*x^72 + 20*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 116*x^66 + 69*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 87*x^25 + 84*x^24 + 20*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 12*x^18 + 15*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 17*x^9 + 124*x^8 + 100*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 36*x^2 + x + 116, x^93 + 74*x^91 + 56*x^90 + 67*x^89 + 56*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 104*x^82 + 11*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 61*x^73 + 104*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 120*x^66 + 61*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 79*x^25 + 24*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 8*x^18 + 87*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 57*x^9 + 72*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 24*x^2 + 25*x + 88, x^93 + 74*x^91 + 28*x^90 + 75*x^89 + 108*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 52*x^82 + 67*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 85*x^73 + 36*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 60*x^66 + 101*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 119*x^25 + 92*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 68*x^18 + 111*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 113*x^9 + 20*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 76*x^2 + 33*x + 60, x^93 + 74*x^91 + 3*x^89 + 96*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 102*x^83 + 64*x^82 + 75*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 125*x^73 + 32*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 114*x^67 + 64*x^66 + 125*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 15*x^25 + 96*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 30*x^19 + 64*x^18 + 23*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 121*x^9 + 32*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 106*x^3 + 64*x^2 + 89*x + 32, x^93 + 74*x^91 + 60*x^90 + 11*x^89 + 76*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 20*x^82 + 3*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 21*x^73 + 68*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 92*x^66 + 37*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 55*x^25 + 60*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 36*x^18 + 47*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 49*x^9 + 52*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 108*x^2 + 97*x + 28, x^93 + 74*x^91 + 64*x^90 + 3*x^89 + 64*x^88 + 4*x^87 + x^85 + 38*x^83 + 64*x^82 + 11*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 125*x^73 + 64*x^72 + 52*x^71 + 7*x^69 + 50*x^67 + 64*x^66 + 61*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 15*x^25 + 64*x^24 + 52*x^23 + 37*x^21 + 94*x^19 + 64*x^18 + 87*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 121*x^9 + 64*x^8 + 4*x^7 + 27*x^5 + 42*x^3 + 64*x^2 + 25*x + 64, x^93 + 74*x^91 + 44*x^90 + 123*x^89 + 12*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 100*x^82 + 19*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 101*x^73 + 4*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 76*x^66 + 85*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 103*x^25 + 124*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 52*x^18 + 127*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 65*x^9 + 116*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 28*x^2 + 81*x + 92, x^93 + 74*x^91 + 96*x^90 + 99*x^89 + 64*x^88 + 4*x^87 + 64*x^86 + 65*x^85 + 38*x^83 + 32*x^82 + 43*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 29*x^73 + 64*x^72 + 52*x^71 + 64*x^70 + 71*x^69 + 50*x^67 + 96*x^66 + 29*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 111*x^25 + 64*x^24 + 52*x^23 + 64*x^22 + 101*x^21 + 94*x^19 + 32*x^18 + 119*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 25*x^9 + 64*x^8 + 4*x^7 + 64*x^6 + 91*x^5 + 42*x^3 + 96*x^2 + 121*x + 64, x^93 + 74*x^91 + 92*x^90 + 43*x^89 + 12*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 52*x^82 + 35*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 117*x^73 + 4*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 60*x^66 + 5*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 87*x^25 + 124*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 68*x^18 + 79*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 17*x^9 + 116*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 76*x^2 + 65*x + 28, x^93 + 74*x^91 + 64*x^90 + 67*x^89 + 32*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 102*x^83 + 11*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 61*x^73 + 96*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 114*x^67 + 61*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 79*x^25 + 32*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 30*x^19 + 87*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 57*x^9 + 96*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 106*x^3 + 25*x + 96, x^93 + 74*x^91 + 84*x^90 + 91*x^89 + 84*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 92*x^82 + 115*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 5*x^73 + 28*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 116*x^66 + 117*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 71*x^25 + 100*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 12*x^18 + 95*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 97*x^9 + 44*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 36*x^2 + 113*x + 68, x^93 + 74*x^91 + 116*x^90 + 11*x^89 + 4*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 60*x^82 + 67*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 21*x^73 + 44*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 20*x^66 + 101*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 55*x^25 + 84*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 108*x^18 + 111*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 49*x^9 + 124*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 68*x^2 + 33*x + 52, x^93 + 74*x^91 + 28*x^90 + 27*x^89 + 28*x^88 + 36*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 70*x^83 + 52*x^82 + 115*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 69*x^73 + 52*x^72 + 84*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 82*x^67 + 60*x^66 + 117*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 7*x^25 + 76*x^24 + 84*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 126*x^19 + 68*x^18 + 95*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 33*x^9 + 100*x^8 + 36*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 74*x^3 + 76*x^2 + 113*x + 44, x^93 + 74*x^91 + 112*x^90 + 3*x^89 + 80*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 16*x^82 + 75*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 125*x^73 + 112*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 48*x^66 + 125*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 15*x^25 + 16*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 80*x^18 + 23*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 121*x^9 + 48*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 112*x^2 + 89*x + 80, x^93 + 74*x^91 + 104*x^90 + 99*x^89 + 8*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 56*x^82 + 43*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 29*x^73 + 88*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 104*x^66 + 29*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 111*x^25 + 40*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 24*x^18 + 119*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 25*x^9 + 120*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 72*x^2 + 121*x + 40, x^93 + 74*x^91 + 40*x^90 + 99*x^89 + 104*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 120*x^82 + 43*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 29*x^73 + 120*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 40*x^66 + 29*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 111*x^25 + 8*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 88*x^18 + 119*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 25*x^9 + 24*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 8*x^2 + 121*x + 8, x^93 + 74*x^91 + 4*x^90 + 59*x^89 + 100*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 44*x^82 + 83*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 37*x^73 + 76*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 100*x^66 + 21*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 39*x^25 + 52*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 28*x^18 + 63*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + x^9 + 28*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 84*x^2 + 17*x + 84, x^93 + 74*x^91 + 67*x^89 + 32*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 102*x^83 + 64*x^82 + 11*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 61*x^73 + 96*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 114*x^67 + 64*x^66 + 61*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 79*x^25 + 32*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 30*x^19 + 64*x^18 + 87*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 57*x^9 + 96*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 106*x^3 + 64*x^2 + 25*x + 96, x^93 + 74*x^91 + 108*x^90 + 27*x^89 + 108*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 36*x^82 + 115*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 69*x^73 + 36*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 12*x^66 + 117*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 7*x^25 + 92*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 116*x^18 + 95*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 33*x^9 + 20*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 92*x^2 + 113*x + 60, x^93 + 74*x^91 + 16*x^90 + 115*x^89 + 68*x^87 + 96*x^86 + 97*x^85 + 102*x^83 + 48*x^82 + 27*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 77*x^73 + 116*x^71 + 96*x^70 + 103*x^69 + 114*x^67 + 16*x^66 + 109*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 63*x^25 + 116*x^23 + 96*x^22 + 5*x^21 + 30*x^19 + 112*x^18 + 39*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 9*x^9 + 68*x^7 + 96*x^6 + 123*x^5 + 106*x^3 + 80*x^2 + 9*x, x^93 + 74*x^91 + 104*x^90 + 35*x^89 + 8*x^88 + 68*x^87 + 112*x^86 + x^85 + 112*x^84 + 102*x^83 + 120*x^82 + 43*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 93*x^73 + 88*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 40*x^66 + 29*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 47*x^25 + 40*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 88*x^18 + 119*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 89*x^9 + 120*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 8*x^2 + 121*x + 104, x^93 + 74*x^91 + 44*x^90 + 91*x^89 + 12*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 36*x^82 + 115*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 5*x^73 + 4*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 12*x^66 + 117*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 71*x^25 + 124*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 116*x^18 + 95*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 97*x^9 + 116*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 92*x^2 + 113*x + 28, x^93 + 74*x^91 + 108*x^90 + 91*x^89 + 44*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 36*x^82 + 51*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 5*x^73 + 100*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 12*x^66 + 53*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 71*x^25 + 28*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 116*x^18 + 31*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 97*x^9 + 84*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 92*x^2 + 49*x + 124, x^93 + 74*x^91 + 104*x^90 + 19*x^89 + 88*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 120*x^82 + 59*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 45*x^73 + 72*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 40*x^66 + 77*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 95*x^25 + 56*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 88*x^18 + 71*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 105*x^9 + 40*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 8*x^2 + 105*x + 120, x^93 + 74*x^91 + 112*x^90 + 83*x^89 + 64*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 16*x^82 + 123*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 109*x^73 + 64*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 48*x^66 + 13*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 31*x^25 + 64*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 80*x^18 + 7*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 41*x^9 + 64*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 112*x^2 + 41*x, x^93 + 74*x^91 + 12*x^90 + 11*x^89 + 60*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 68*x^82 + 67*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 21*x^73 + 20*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 108*x^66 + 101*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 55*x^25 + 108*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 20*x^18 + 111*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 49*x^9 + 68*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 60*x^2 + 33*x + 12, x^93 + 74*x^91 + 64*x^90 + 83*x^89 + 16*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 38*x^83 + 123*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 109*x^73 + 48*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 50*x^67 + 13*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 31*x^25 + 80*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 94*x^19 + 7*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 41*x^9 + 112*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 42*x^3 + 41*x + 16, x^93 + 74*x^91 + 28*x^90 + 59*x^89 + 60*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 116*x^82 + 19*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 37*x^73 + 20*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 124*x^66 + 85*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 39*x^25 + 108*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 4*x^18 + 127*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + x^9 + 68*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 12*x^2 + 81*x + 12, x^93 + 74*x^91 + 120*x^90 + 67*x^89 + 56*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 40*x^82 + 11*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 61*x^73 + 104*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 56*x^66 + 61*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 79*x^25 + 24*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 72*x^18 + 87*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 57*x^9 + 72*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 88*x^2 + 25*x + 88, x^93 + 74*x^91 + 12*x^90 + 123*x^89 + 108*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 4*x^82 + 19*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 101*x^73 + 36*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 44*x^66 + 85*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 103*x^25 + 92*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 84*x^18 + 127*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 65*x^9 + 20*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 124*x^2 + 81*x + 60, x^93 + 74*x^91 + 68*x^90 + 27*x^89 + 68*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 44*x^82 + 51*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 69*x^73 + 108*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 100*x^66 + 53*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 7*x^25 + 20*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 28*x^18 + 31*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 33*x^9 + 60*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 84*x^2 + 49*x + 116, x^93 + 74*x^91 + 60*x^90 + 27*x^89 + 124*x^88 + 36*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 70*x^83 + 20*x^82 + 115*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 69*x^73 + 84*x^72 + 84*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 82*x^67 + 92*x^66 + 117*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 7*x^25 + 44*x^24 + 84*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 126*x^19 + 36*x^18 + 95*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 33*x^9 + 4*x^8 + 36*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 74*x^3 + 108*x^2 + 113*x + 12, x^93 + 74*x^91 + 84*x^90 + 27*x^89 + 20*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 28*x^82 + 115*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 69*x^73 + 92*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 52*x^66 + 117*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 7*x^25 + 36*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 76*x^18 + 95*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 33*x^9 + 108*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 100*x^2 + 113*x + 68, x^93 + 74*x^91 + 120*x^90 + 67*x^89 + 120*x^88 + 4*x^87 + 16*x^86 + x^85 + 80*x^84 + 38*x^83 + 104*x^82 + 75*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 61*x^73 + 40*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 120*x^66 + 125*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 79*x^25 + 88*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 8*x^18 + 23*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 57*x^9 + 8*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 24*x^2 + 89*x + 88, x^93 + 74*x^91 + 83*x^89 + 16*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 38*x^83 + 64*x^82 + 123*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 109*x^73 + 48*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 50*x^67 + 64*x^66 + 13*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 31*x^25 + 80*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 94*x^19 + 64*x^18 + 7*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 41*x^9 + 112*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 42*x^3 + 64*x^2 + 41*x + 16, x^93 + 74*x^91 + 24*x^90 + 83*x^89 + 104*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 8*x^82 + 123*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 109*x^73 + 120*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 88*x^66 + 13*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 31*x^25 + 8*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 40*x^18 + 7*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 41*x^9 + 24*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 120*x^2 + 41*x + 72, x^93 + 74*x^91 + 44*x^90 + 27*x^89 + 44*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 70*x^83 + 100*x^82 + 115*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 69*x^73 + 100*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 82*x^67 + 76*x^66 + 117*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 7*x^25 + 28*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 126*x^19 + 52*x^18 + 95*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 33*x^9 + 84*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 74*x^3 + 28*x^2 + 113*x + 124, x^93 + 74*x^91 + 8*x^90 + 3*x^89 + 104*x^88 + 4*x^87 + 112*x^86 + x^85 + 112*x^84 + 38*x^83 + 24*x^82 + 11*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 125*x^73 + 120*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 8*x^66 + 61*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 15*x^25 + 8*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 120*x^18 + 87*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 121*x^9 + 24*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 104*x^2 + 25*x + 8, x^93 + 74*x^91 + 68*x^90 + 59*x^89 + 68*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 108*x^82 + 83*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 37*x^73 + 108*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 36*x^66 + 21*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 39*x^25 + 20*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 92*x^18 + 63*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + x^9 + 60*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 20*x^2 + 17*x + 52, x^93 + 74*x^91 + 76*x^90 + 43*x^89 + 124*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 4*x^82 + 35*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 117*x^73 + 84*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 44*x^66 + 5*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 87*x^25 + 44*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 84*x^18 + 79*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 17*x^9 + 4*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 124*x^2 + 65*x + 76, x^93 + 74*x^91 + 92*x^90 + 11*x^89 + 108*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 116*x^82 + 3*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 21*x^73 + 36*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 124*x^66 + 37*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 55*x^25 + 92*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 4*x^18 + 47*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 49*x^9 + 20*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 12*x^2 + 97*x + 60, x^93 + 74*x^91 + 72*x^90 + 99*x^89 + 104*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 38*x^83 + 88*x^82 + 43*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 29*x^73 + 120*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 50*x^67 + 72*x^66 + 29*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 111*x^25 + 8*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 94*x^19 + 56*x^18 + 119*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 25*x^9 + 24*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 42*x^3 + 40*x^2 + 121*x + 8, x^93 + 74*x^91 + 76*x^90 + 43*x^89 + 28*x^88 + 36*x^87 + 8*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 4*x^82 + 35*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 117*x^73 + 52*x^72 + 84*x^71 + 40*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 44*x^66 + 5*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 87*x^25 + 76*x^24 + 84*x^23 + 104*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 84*x^18 + 79*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 17*x^9 + 100*x^8 + 36*x^7 + 72*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 124*x^2 + 65*x + 108, x^93 + 74*x^91 + 92*x^90 + 107*x^89 + 12*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 52*x^82 + 99*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 53*x^73 + 4*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 60*x^66 + 69*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 23*x^25 + 124*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 68*x^18 + 15*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 81*x^9 + 116*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 76*x^2 + x + 28, x^93 + 74*x^91 + 116*x^90 + 27*x^89 + 116*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 124*x^82 + 115*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 69*x^73 + 124*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 84*x^66 + 117*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 7*x^25 + 4*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 44*x^18 + 95*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 33*x^9 + 12*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 4*x^2 + 113*x + 36, x^93 + 74*x^91 + 56*x^90 + 3*x^89 + 24*x^88 + 4*x^87 + 16*x^86 + x^85 + 16*x^84 + 38*x^83 + 40*x^82 + 11*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 125*x^73 + 8*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 56*x^66 + 61*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 15*x^25 + 120*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 72*x^18 + 87*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 121*x^9 + 104*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 88*x^2 + 25*x + 120, x^93 + 74*x^91 + 3*x^89 + 96*x^88 + 4*x^87 + x^85 + 64*x^84 + 38*x^83 + 11*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 125*x^73 + 32*x^72 + 52*x^71 + 7*x^69 + 64*x^68 + 50*x^67 + 61*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 15*x^25 + 96*x^24 + 52*x^23 + 37*x^21 + 64*x^20 + 94*x^19 + 87*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 121*x^9 + 32*x^8 + 4*x^7 + 27*x^5 + 64*x^4 + 42*x^3 + 25*x + 96, x^93 + 74*x^91 + 20*x^90 + 59*x^89 + 116*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 92*x^82 + 83*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 37*x^73 + 124*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 116*x^66 + 21*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 39*x^25 + 4*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 12*x^18 + 63*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + x^9 + 12*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 36*x^2 + 17*x + 36, x^93 + 74*x^91 + 76*x^90 + 11*x^89 + 60*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 68*x^82 + 3*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 21*x^73 + 20*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 108*x^66 + 37*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 55*x^25 + 108*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 20*x^18 + 47*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 49*x^9 + 68*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 60*x^2 + 97*x + 76, x^93 + 74*x^91 + 80*x^90 + 115*x^89 + 4*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 48*x^82 + 91*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 77*x^73 + 52*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 16*x^66 + 45*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 63*x^25 + 52*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 112*x^18 + 103*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 9*x^9 + 4*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 80*x^2 + 73*x + 64, x^93 + 74*x^91 + 8*x^90 + 115*x^89 + 88*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 88*x^82 + 91*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 77*x^73 + 72*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 72*x^66 + 45*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 63*x^25 + 56*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 56*x^18 + 103*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 9*x^9 + 40*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 40*x^2 + 73*x + 120, x^93 + 74*x^91 + 20*x^90 + 11*x^89 + 4*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 92*x^82 + 3*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 21*x^73 + 44*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 116*x^66 + 37*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 55*x^25 + 84*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 12*x^18 + 47*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 49*x^9 + 124*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 36*x^2 + 97*x + 116, x^93 + 74*x^91 + 36*x^90 + 107*x^89 + 20*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 12*x^82 + 35*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 53*x^73 + 92*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 4*x^66 + 5*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 23*x^25 + 36*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 124*x^18 + 79*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 81*x^9 + 108*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 116*x^2 + 65*x + 68, x^93 + 74*x^91 + 88*x^90 + 35*x^89 + 56*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 8*x^82 + 107*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 93*x^73 + 104*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 88*x^66 + 93*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 47*x^25 + 24*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 40*x^18 + 55*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 89*x^9 + 72*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 120*x^2 + 57*x + 24, x^93 + 74*x^91 + 24*x^90 + 51*x^89 + 104*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 72*x^82 + 91*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 13*x^73 + 120*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 24*x^66 + 45*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 127*x^25 + 8*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 104*x^18 + 103*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 73*x^9 + 24*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 56*x^2 + 73*x + 8, x^93 + 74*x^91 + 60*x^90 + 75*x^89 + 44*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 84*x^82 + 3*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 85*x^73 + 100*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 28*x^66 + 37*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 119*x^25 + 28*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 100*x^18 + 47*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 113*x^9 + 84*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 44*x^2 + 97*x + 60, x^93 + 74*x^91 + 112*x^90 + 99*x^89 + 16*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 80*x^82 + 43*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 29*x^73 + 48*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 112*x^66 + 29*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 111*x^25 + 80*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 16*x^18 + 119*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 25*x^9 + 112*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 48*x^2 + 121*x + 80, x^93 + 74*x^91 + 108*x^90 + 59*x^89 + 108*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 100*x^82 + 19*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 37*x^73 + 36*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 76*x^66 + 85*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 39*x^25 + 92*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 52*x^18 + 127*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + x^9 + 20*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 28*x^2 + 81*x + 124, x^93 + 74*x^91 + 24*x^90 + 99*x^89 + 24*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 72*x^82 + 43*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 29*x^73 + 8*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 24*x^66 + 29*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 111*x^25 + 120*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 104*x^18 + 119*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 25*x^9 + 104*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 56*x^2 + 121*x + 120, x^93 + 74*x^91 + 4*x^90 + 91*x^89 + 4*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 44*x^82 + 51*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 5*x^73 + 44*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 100*x^66 + 53*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 71*x^25 + 84*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 28*x^18 + 31*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 97*x^9 + 124*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 84*x^2 + 49*x + 116, x^93 + 74*x^91 + 88*x^90 + 83*x^89 + 104*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 8*x^82 + 59*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 109*x^73 + 120*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 88*x^66 + 77*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 31*x^25 + 8*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 40*x^18 + 71*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 41*x^9 + 24*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 120*x^2 + 105*x + 8, x^93 + 74*x^91 + 36*x^90 + 123*x^89 + 36*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 76*x^82 + 83*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 101*x^73 + 12*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 68*x^66 + 21*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 103*x^25 + 116*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 60*x^18 + 63*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 65*x^9 + 92*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 52*x^2 + 17*x + 84, x^93 + 74*x^91 + 72*x^90 + 67*x^89 + 72*x^88 + 4*x^87 + 112*x^86 + x^85 + 48*x^84 + 38*x^83 + 88*x^82 + 75*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 61*x^73 + 24*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 72*x^66 + 125*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 79*x^25 + 104*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 56*x^18 + 23*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 57*x^9 + 56*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 40*x^2 + 89*x + 104, x^93 + 74*x^91 + 124*x^90 + 91*x^89 + 60*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 20*x^82 + 115*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 5*x^73 + 20*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 92*x^66 + 117*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 71*x^25 + 108*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 36*x^18 + 95*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 97*x^9 + 68*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 108*x^2 + 113*x + 12, x^93 + 74*x^91 + 76*x^90 + 75*x^89 + 60*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 4*x^82 + 3*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 85*x^73 + 20*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 44*x^66 + 37*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 119*x^25 + 108*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 84*x^18 + 47*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 113*x^9 + 68*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 124*x^2 + 97*x + 12, x^93 + 74*x^91 + 52*x^90 + 43*x^89 + 36*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 60*x^82 + 99*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 117*x^73 + 12*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 20*x^66 + 69*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 87*x^25 + 116*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 108*x^18 + 15*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 17*x^9 + 92*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 68*x^2 + x + 20, x^93 + 74*x^91 + 116*x^90 + 59*x^89 + 20*x^88 + 100*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 60*x^82 + 19*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 37*x^73 + 92*x^72 + 20*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 20*x^66 + 85*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 39*x^25 + 36*x^24 + 20*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 108*x^18 + 127*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + x^9 + 108*x^8 + 100*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 68*x^2 + 81*x + 4, x^93 + 74*x^91 + 40*x^90 + 3*x^89 + 40*x^88 + 4*x^87 + 48*x^86 + x^85 + 112*x^84 + 38*x^83 + 120*x^82 + 11*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 125*x^73 + 56*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 40*x^66 + 61*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 15*x^25 + 72*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 88*x^18 + 87*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 121*x^9 + 88*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 8*x^2 + 25*x + 72, x^93 + 74*x^91 + 36*x^90 + 59*x^89 + 36*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 76*x^82 + 19*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 37*x^73 + 12*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 68*x^66 + 85*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 39*x^25 + 116*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 60*x^18 + 127*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + x^9 + 92*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 52*x^2 + 81*x + 84, x^93 + 74*x^91 + 124*x^90 + 123*x^89 + 124*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 84*x^82 + 19*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 101*x^73 + 84*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 28*x^66 + 85*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 103*x^25 + 44*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 100*x^18 + 127*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 65*x^9 + 4*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 44*x^2 + 81*x + 12, x^93 + 74*x^91 + 52*x^90 + 43*x^89 + 36*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 124*x^82 + 35*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 117*x^73 + 12*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 84*x^66 + 5*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 87*x^25 + 116*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 44*x^18 + 79*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 17*x^9 + 92*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 4*x^2 + 65*x + 84, x^93 + 74*x^91 + 76*x^90 + 123*x^89 + 12*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 4*x^82 + 83*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 101*x^73 + 4*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 44*x^66 + 21*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 103*x^25 + 124*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 84*x^18 + 63*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 65*x^9 + 116*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 124*x^2 + 17*x + 28, x^93 + 74*x^91 + 44*x^90 + 59*x^89 + 76*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 100*x^82 + 83*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 37*x^73 + 68*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 76*x^66 + 21*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 39*x^25 + 60*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 52*x^18 + 63*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + x^9 + 52*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 28*x^2 + 17*x + 28, x^93 + 74*x^91 + 96*x^90 + 115*x^89 + 48*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 102*x^83 + 32*x^82 + 27*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 77*x^73 + 16*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 114*x^67 + 96*x^66 + 109*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 63*x^25 + 112*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 30*x^19 + 32*x^18 + 39*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 9*x^9 + 80*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 106*x^3 + 96*x^2 + 9*x + 112, x^93 + 74*x^91 + 24*x^90 + 83*x^89 + 40*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 8*x^82 + 123*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 109*x^73 + 56*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 88*x^66 + 13*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 31*x^25 + 72*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 40*x^18 + 7*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 41*x^9 + 88*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 120*x^2 + 41*x + 8, x^93 + 74*x^91 + 112*x^90 + 67*x^89 + 48*x^88 + 4*x^87 + 32*x^86 + x^85 + 32*x^84 + 38*x^83 + 80*x^82 + 75*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 61*x^73 + 16*x^72 + 52*x^71 + 32*x^70 + 7*x^69 + 32*x^68 + 50*x^67 + 112*x^66 + 125*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 79*x^25 + 112*x^24 + 52*x^23 + 32*x^22 + 37*x^21 + 32*x^20 + 94*x^19 + 16*x^18 + 23*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 57*x^9 + 80*x^8 + 4*x^7 + 32*x^6 + 27*x^5 + 32*x^4 + 42*x^3 + 48*x^2 + 89*x + 112, x^93 + 74*x^91 + 68*x^90 + 75*x^89 + 52*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 108*x^82 + 67*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 85*x^73 + 60*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 36*x^66 + 101*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 119*x^25 + 68*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 92*x^18 + 111*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 113*x^9 + 76*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 20*x^2 + 33*x + 100, x^93 + 74*x^91 + 72*x^90 + 115*x^89 + 88*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 102*x^83 + 88*x^82 + 27*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 77*x^73 + 72*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 114*x^67 + 72*x^66 + 109*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 63*x^25 + 56*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 30*x^19 + 56*x^18 + 39*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 9*x^9 + 40*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 106*x^3 + 40*x^2 + 9*x + 56, x^93 + 74*x^91 + 80*x^90 + 51*x^89 + 68*x^87 + 96*x^86 + 97*x^85 + 102*x^83 + 112*x^82 + 91*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 112*x^74 + 13*x^73 + 116*x^71 + 96*x^70 + 103*x^69 + 114*x^67 + 80*x^66 + 45*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 127*x^25 + 116*x^23 + 96*x^22 + 5*x^21 + 30*x^19 + 48*x^18 + 103*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 48*x^10 + 73*x^9 + 68*x^7 + 96*x^6 + 123*x^5 + 106*x^3 + 16*x^2 + 73*x, x^93 + 74*x^91 + 120*x^90 + 3*x^89 + 88*x^88 + 68*x^87 + 80*x^86 + 65*x^85 + 80*x^84 + 102*x^83 + 40*x^82 + 75*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 125*x^73 + 72*x^72 + 116*x^71 + 16*x^70 + 71*x^69 + 16*x^68 + 114*x^67 + 56*x^66 + 125*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 15*x^25 + 56*x^24 + 116*x^23 + 16*x^22 + 101*x^21 + 16*x^20 + 30*x^19 + 72*x^18 + 23*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 121*x^9 + 40*x^8 + 68*x^7 + 80*x^6 + 91*x^5 + 80*x^4 + 106*x^3 + 88*x^2 + 89*x + 120, x^93 + 74*x^91 + 4*x^90 + 123*x^89 + 4*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 44*x^82 + 19*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 101*x^73 + 44*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 100*x^66 + 85*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 103*x^25 + 84*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 28*x^18 + 127*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 65*x^9 + 124*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 84*x^2 + 81*x + 116, x^93 + 74*x^91 + 60*x^90 + 91*x^89 + 92*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 84*x^82 + 115*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 5*x^73 + 116*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 28*x^66 + 117*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 71*x^25 + 12*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 100*x^18 + 95*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 97*x^9 + 36*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 44*x^2 + 113*x + 44, x^93 + 74*x^91 + 16*x^90 + 35*x^89 + 16*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 48*x^82 + 107*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 93*x^73 + 48*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 16*x^66 + 93*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 47*x^25 + 80*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 112*x^18 + 55*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 89*x^9 + 112*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 80*x^2 + 57*x + 80, x^93 + 74*x^91 + 120*x^90 + 19*x^89 + 40*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 40*x^82 + 59*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 45*x^73 + 56*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 56*x^66 + 77*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 95*x^25 + 72*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 72*x^18 + 71*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 105*x^9 + 88*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 88*x^2 + 105*x + 8, x^93 + 74*x^91 + 120*x^90 + 19*x^89 + 104*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 48*x^84 + 38*x^83 + 40*x^82 + 59*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 45*x^73 + 120*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 112*x^68 + 50*x^67 + 56*x^66 + 77*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 95*x^25 + 8*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 112*x^20 + 94*x^19 + 72*x^18 + 71*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 105*x^9 + 24*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 48*x^4 + 42*x^3 + 88*x^2 + 105*x + 72, x^93 + 74*x^91 + 24*x^90 + 51*x^89 + 40*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 72*x^82 + 91*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 13*x^73 + 56*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 24*x^66 + 45*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 127*x^25 + 72*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 104*x^18 + 103*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 73*x^9 + 88*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 56*x^2 + 73*x + 72, x^93 + 74*x^91 + 28*x^90 + 107*x^89 + 12*x^88 + 36*x^87 + 104*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 116*x^82 + 99*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 53*x^73 + 4*x^72 + 84*x^71 + 8*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 124*x^66 + 69*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 23*x^25 + 124*x^24 + 84*x^23 + 72*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 4*x^18 + 15*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 81*x^9 + 116*x^8 + 36*x^7 + 40*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 12*x^2 + x + 28, x^93 + 74*x^91 + 48*x^90 + 83*x^89 + 96*x^88 + 68*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 102*x^83 + 16*x^82 + 59*x^81 + 32*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 109*x^73 + 32*x^72 + 116*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 114*x^67 + 48*x^66 + 77*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 31*x^25 + 96*x^24 + 116*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 30*x^19 + 80*x^18 + 71*x^17 + 32*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 41*x^9 + 32*x^8 + 68*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 106*x^3 + 112*x^2 + 105*x + 96, x^93 + 74*x^91 + 112*x^90 + 99*x^89 + 80*x^88 + 4*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 38*x^83 + 80*x^82 + 43*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 29*x^73 + 112*x^72 + 52*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 50*x^67 + 112*x^66 + 29*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 111*x^25 + 16*x^24 + 52*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 94*x^19 + 16*x^18 + 119*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 25*x^9 + 48*x^8 + 4*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 42*x^3 + 48*x^2 + 121*x + 16, x^93 + 74*x^91 + 76*x^90 + 27*x^89 + 44*x^88 + 100*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 4*x^82 + 51*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 69*x^73 + 100*x^72 + 20*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 44*x^66 + 53*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 7*x^25 + 28*x^24 + 20*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 84*x^18 + 31*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 33*x^9 + 84*x^8 + 100*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 124*x^2 + 49*x + 60, x^93 + 74*x^91 + 100*x^90 + 27*x^89 + 4*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 76*x^82 + 115*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 69*x^73 + 44*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 68*x^66 + 117*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 7*x^25 + 84*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 60*x^18 + 95*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 33*x^9 + 124*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 52*x^2 + 113*x + 116, x^93 + 74*x^91 + 116*x^90 + 11*x^89 + 4*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 124*x^82 + 3*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 21*x^73 + 44*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 84*x^66 + 37*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 55*x^25 + 84*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 44*x^18 + 47*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 49*x^9 + 124*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 4*x^2 + 97*x + 116, x^93 + 74*x^91 + 56*x^90 + 67*x^89 + 120*x^88 + 4*x^87 + 16*x^86 + x^85 + 80*x^84 + 38*x^83 + 40*x^82 + 75*x^81 + 40*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 61*x^73 + 40*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 50*x^67 + 56*x^66 + 125*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 79*x^25 + 88*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 94*x^19 + 72*x^18 + 23*x^17 + 72*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 57*x^9 + 8*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 42*x^3 + 88*x^2 + 89*x + 88, x^93 + 74*x^91 + 64*x^90 + 35*x^89 + 68*x^87 + 64*x^86 + x^85 + 64*x^84 + 102*x^83 + 43*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 93*x^73 + 116*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 114*x^67 + 29*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 47*x^25 + 116*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 30*x^19 + 119*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 89*x^9 + 68*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 106*x^3 + 121*x + 64, x^93 + 74*x^91 + 68*x^90 + 75*x^89 + 20*x^88 + 100*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 108*x^82 + 67*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 85*x^73 + 92*x^72 + 20*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 36*x^66 + 101*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 119*x^25 + 36*x^24 + 20*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 92*x^18 + 111*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 113*x^9 + 108*x^8 + 100*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 20*x^2 + 33*x + 68, x^93 + 74*x^91 + 28*x^90 + 75*x^89 + 76*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 52*x^82 + 67*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 85*x^73 + 68*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 60*x^66 + 101*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 119*x^25 + 60*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 68*x^18 + 111*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 113*x^9 + 52*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 76*x^2 + 33*x + 28, x^93 + 74*x^91 + 116*x^90 + 91*x^89 + 20*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 124*x^82 + 51*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 5*x^73 + 92*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 84*x^66 + 53*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 71*x^25 + 36*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 44*x^18 + 31*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 97*x^9 + 108*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 4*x^2 + 49*x + 68, x^93 + 74*x^91 + 76*x^90 + 75*x^89 + 92*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 68*x^82 + 67*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 85*x^73 + 116*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 108*x^66 + 101*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 119*x^25 + 12*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 20*x^18 + 111*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 113*x^9 + 36*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 60*x^2 + 33*x + 108, x^93 + 74*x^91 + 96*x^90 + 115*x^89 + 48*x^88 + 4*x^87 + 33*x^85 + 96*x^84 + 38*x^83 + 96*x^82 + 91*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 77*x^73 + 16*x^72 + 52*x^71 + 39*x^69 + 96*x^68 + 50*x^67 + 32*x^66 + 45*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 63*x^25 + 112*x^24 + 52*x^23 + 69*x^21 + 96*x^20 + 94*x^19 + 96*x^18 + 103*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 9*x^9 + 80*x^8 + 4*x^7 + 59*x^5 + 96*x^4 + 42*x^3 + 32*x^2 + 73*x + 48, x^93 + 74*x^91 + 4*x^90 + 75*x^89 + 116*x^88 + 36*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 70*x^83 + 108*x^82 + 3*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 85*x^73 + 124*x^72 + 84*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 82*x^67 + 36*x^66 + 37*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 119*x^25 + 4*x^24 + 84*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 126*x^19 + 92*x^18 + 47*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 113*x^9 + 12*x^8 + 36*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 74*x^3 + 20*x^2 + 97*x + 100, x^93 + 74*x^91 + 92*x^90 + 75*x^89 + 76*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 52*x^82 + 3*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 85*x^73 + 68*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 60*x^66 + 37*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 119*x^25 + 60*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 68*x^18 + 47*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 113*x^9 + 52*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 76*x^2 + 97*x + 92, x^93 + 74*x^91 + 35*x^89 + 68*x^87 + 64*x^86 + x^85 + 64*x^84 + 102*x^83 + 64*x^82 + 43*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 93*x^73 + 116*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 114*x^67 + 64*x^66 + 29*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 47*x^25 + 116*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 30*x^19 + 64*x^18 + 119*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 89*x^9 + 68*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 106*x^3 + 64*x^2 + 121*x + 64, x^93 + 74*x^91 + 68*x^90 + 59*x^89 + 4*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 108*x^82 + 83*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 37*x^73 + 44*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 36*x^66 + 21*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 39*x^25 + 84*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 92*x^18 + 63*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + x^9 + 124*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 20*x^2 + 17*x + 116, x^93 + 74*x^91 + 52*x^90 + 107*x^89 + 36*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 124*x^82 + 99*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 53*x^73 + 12*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 84*x^66 + 69*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 23*x^25 + 116*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 44*x^18 + 15*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 81*x^9 + 92*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 4*x^2 + x + 84, x^93 + 74*x^91 + 64*x^90 + 83*x^89 + 80*x^88 + 4*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 38*x^83 + 123*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 109*x^73 + 112*x^72 + 52*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 50*x^67 + 13*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 31*x^25 + 16*x^24 + 52*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 94*x^19 + 7*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 41*x^9 + 48*x^8 + 4*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 42*x^3 + 41*x + 80, x^93 + 74*x^91 + 72*x^90 + 99*x^89 + 40*x^88 + 68*x^87 + 48*x^86 + x^85 + 48*x^84 + 102*x^83 + 24*x^82 + 107*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 29*x^73 + 56*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 8*x^66 + 93*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 111*x^25 + 72*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 120*x^18 + 55*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 25*x^9 + 88*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 104*x^2 + 57*x + 8, x^93 + 74*x^91 + 92*x^90 + 59*x^89 + 92*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 116*x^82 + 83*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 37*x^73 + 116*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 124*x^66 + 21*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 39*x^25 + 12*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 4*x^18 + 63*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + x^9 + 36*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 12*x^2 + 17*x + 108, x^93 + 74*x^91 + 12*x^90 + 75*x^89 + 60*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 4*x^82 + 67*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 85*x^73 + 20*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 44*x^66 + 101*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 119*x^25 + 108*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 84*x^18 + 111*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 113*x^9 + 68*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 124*x^2 + 33*x + 76, x^93 + 74*x^91 + 48*x^90 + 35*x^89 + 112*x^88 + 68*x^87 + 96*x^86 + x^85 + 96*x^84 + 102*x^83 + 80*x^82 + 43*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 93*x^73 + 80*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 112*x^66 + 29*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 47*x^25 + 48*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 16*x^18 + 119*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 89*x^9 + 16*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 48*x^2 + 121*x + 112, x^93 + 74*x^91 + 88*x^90 + 51*x^89 + 72*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 72*x^82 + 27*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 13*x^73 + 24*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 24*x^66 + 109*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 127*x^25 + 104*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 104*x^18 + 39*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 73*x^9 + 56*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 56*x^2 + 9*x + 40, x^93 + 74*x^91 + 92*x^90 + 27*x^89 + 60*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 52*x^82 + 51*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 69*x^73 + 20*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 60*x^66 + 53*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 7*x^25 + 108*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 68*x^18 + 31*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 33*x^9 + 68*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 76*x^2 + 49*x + 12, x^93 + 74*x^91 + 64*x^90 + 83*x^89 + 48*x^88 + 68*x^87 + 33*x^85 + 32*x^84 + 102*x^83 + 64*x^82 + 59*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 64*x^74 + 109*x^73 + 16*x^72 + 116*x^71 + 39*x^69 + 32*x^68 + 114*x^67 + 64*x^66 + 77*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 30*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 78*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 90*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 122*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 31*x^25 + 112*x^24 + 116*x^23 + 69*x^21 + 32*x^20 + 30*x^19 + 64*x^18 + 71*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 64*x^10 + 41*x^9 + 80*x^8 + 68*x^7 + 59*x^5 + 32*x^4 + 106*x^3 + 64*x^2 + 105*x + 112, x^93 + 74*x^91 + 20*x^90 + 123*x^89 + 52*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 28*x^82 + 83*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 101*x^73 + 60*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 52*x^66 + 21*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 103*x^25 + 68*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 76*x^18 + 63*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + 65*x^9 + 76*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 100*x^2 + 17*x + 36, x^93 + 74*x^91 + 32*x^90 + 115*x^89 + 112*x^88 + 68*x^87 + 64*x^86 + 97*x^85 + 32*x^84 + 102*x^83 + 96*x^82 + 27*x^81 + 80*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 96*x^74 + 77*x^73 + 80*x^72 + 116*x^71 + 64*x^70 + 103*x^69 + 32*x^68 + 114*x^67 + 32*x^66 + 109*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 63*x^25 + 48*x^24 + 116*x^23 + 64*x^22 + 5*x^21 + 32*x^20 + 30*x^19 + 96*x^18 + 39*x^17 + 16*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 96*x^10 + 9*x^9 + 16*x^8 + 68*x^7 + 64*x^6 + 123*x^5 + 32*x^4 + 106*x^3 + 32*x^2 + 9*x + 48, x^93 + 74*x^91 + 120*x^90 + 19*x^89 + 72*x^88 + 4*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 40*x^82 + 59*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 45*x^73 + 24*x^72 + 52*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 56*x^66 + 77*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 95*x^25 + 104*x^24 + 52*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 72*x^18 + 71*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 105*x^9 + 56*x^8 + 4*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 88*x^2 + 105*x + 40, x^93 + 74*x^91 + 108*x^90 + 123*x^89 + 76*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 36*x^82 + 19*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 101*x^73 + 68*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 12*x^66 + 85*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 103*x^25 + 60*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 116*x^18 + 127*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 65*x^9 + 52*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 92*x^2 + 81*x + 28, x^93 + 74*x^91 + 108*x^90 + 43*x^89 + 28*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 100*x^82 + 35*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 117*x^73 + 52*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 76*x^66 + 5*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 87*x^25 + 76*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 52*x^18 + 79*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 17*x^9 + 100*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 28*x^2 + 65*x + 108, x^93 + 74*x^91 + 36*x^90 + 75*x^89 + 20*x^88 + 36*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 70*x^83 + 76*x^82 + 3*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 85*x^73 + 92*x^72 + 84*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 82*x^67 + 68*x^66 + 37*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 119*x^25 + 36*x^24 + 84*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 126*x^19 + 60*x^18 + 47*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 113*x^9 + 108*x^8 + 36*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 74*x^3 + 52*x^2 + 97*x + 4, x^93 + 74*x^91 + 100*x^90 + 59*x^89 + 68*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 70*x^83 + 76*x^82 + 83*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 37*x^73 + 108*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 82*x^67 + 68*x^66 + 21*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 39*x^25 + 20*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 126*x^19 + 60*x^18 + 63*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + x^9 + 60*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 74*x^3 + 52*x^2 + 17*x + 52, x^93 + 74*x^91 + 72*x^90 + 115*x^89 + 56*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 24*x^82 + 91*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 24*x^74 + 77*x^73 + 104*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 8*x^66 + 45*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 63*x^25 + 24*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 120*x^18 + 103*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 56*x^10 + 9*x^9 + 72*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 104*x^2 + 73*x + 88, x^93 + 74*x^91 + 28*x^90 + 123*x^89 + 92*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 116*x^82 + 83*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 101*x^73 + 116*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 124*x^66 + 21*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 103*x^25 + 12*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 4*x^18 + 63*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 65*x^9 + 36*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 12*x^2 + 17*x + 44, x^93 + 74*x^91 + 16*x^90 + 35*x^89 + 112*x^88 + 68*x^87 + 32*x^86 + x^85 + 96*x^84 + 102*x^83 + 112*x^82 + 43*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 93*x^73 + 80*x^72 + 116*x^71 + 32*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 80*x^66 + 29*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 47*x^25 + 48*x^24 + 116*x^23 + 32*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 48*x^18 + 119*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 89*x^9 + 16*x^8 + 68*x^7 + 32*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 16*x^2 + 121*x + 112, x^93 + 74*x^91 + 68*x^90 + 59*x^89 + 36*x^88 + 36*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 108*x^82 + 83*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 37*x^73 + 12*x^72 + 84*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 36*x^66 + 21*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 39*x^25 + 116*x^24 + 84*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 92*x^18 + 63*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + x^9 + 92*x^8 + 36*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 20*x^2 + 17*x + 20, x^93 + 74*x^91 + 24*x^90 + 99*x^89 + 24*x^88 + 68*x^87 + 16*x^86 + x^85 + 80*x^84 + 102*x^83 + 8*x^82 + 107*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 29*x^73 + 8*x^72 + 116*x^71 + 80*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 88*x^66 + 93*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 111*x^25 + 120*x^24 + 116*x^23 + 80*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 40*x^18 + 55*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 25*x^9 + 104*x^8 + 68*x^7 + 16*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 120*x^2 + 57*x + 56, x^93 + 74*x^91 + 116*x^90 + 107*x^89 + 4*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 6*x^83 + 124*x^82 + 35*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 53*x^73 + 44*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 18*x^67 + 84*x^66 + 5*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 23*x^25 + 84*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 62*x^19 + 44*x^18 + 79*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 81*x^9 + 124*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 10*x^3 + 4*x^2 + 65*x + 116, x^93 + 74*x^91 + 52*x^90 + 75*x^89 + 100*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 60*x^82 + 67*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 85*x^73 + 76*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 20*x^66 + 101*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 119*x^25 + 52*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 108*x^18 + 111*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 113*x^9 + 28*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 68*x^2 + 33*x + 84, x^93 + 74*x^91 + 56*x^90 + 51*x^89 + 104*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 40*x^82 + 91*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 13*x^73 + 120*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 56*x^66 + 45*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 127*x^25 + 8*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 72*x^18 + 103*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 73*x^9 + 24*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 88*x^2 + 73*x + 8, x^93 + 74*x^91 + 56*x^90 + 35*x^89 + 120*x^88 + 68*x^87 + 80*x^86 + x^85 + 16*x^84 + 102*x^83 + 104*x^82 + 43*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 93*x^73 + 40*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 114*x^67 + 120*x^66 + 29*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 47*x^25 + 88*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 30*x^19 + 8*x^18 + 119*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 89*x^9 + 8*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 106*x^3 + 24*x^2 + 121*x + 24, x^93 + 74*x^91 + 44*x^90 + 91*x^89 + 76*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 40*x^84 + 6*x^83 + 36*x^82 + 115*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 5*x^73 + 68*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 72*x^68 + 18*x^67 + 12*x^66 + 117*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 71*x^25 + 60*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 8*x^20 + 62*x^19 + 116*x^18 + 95*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 97*x^9 + 52*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 104*x^4 + 10*x^3 + 92*x^2 + 113*x + 92, x^93 + 74*x^91 + 32*x^90 + 3*x^89 + 32*x^88 + 68*x^87 + 65*x^85 + 102*x^83 + 32*x^82 + 75*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 125*x^73 + 96*x^72 + 116*x^71 + 71*x^69 + 114*x^67 + 96*x^66 + 125*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 15*x^25 + 32*x^24 + 116*x^23 + 101*x^21 + 30*x^19 + 32*x^18 + 23*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 121*x^9 + 96*x^8 + 68*x^7 + 91*x^5 + 106*x^3 + 96*x^2 + 89*x + 96, x^93 + 74*x^91 + 104*x^90 + 115*x^89 + 88*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 80*x^84 + 38*x^83 + 120*x^82 + 91*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 77*x^73 + 72*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 16*x^68 + 50*x^67 + 40*x^66 + 45*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 63*x^25 + 56*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 16*x^20 + 94*x^19 + 88*x^18 + 103*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 9*x^9 + 40*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 80*x^4 + 42*x^3 + 8*x^2 + 73*x + 120, x^93 + 74*x^91 + 92*x^90 + 11*x^89 + 76*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 52*x^82 + 67*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 21*x^73 + 68*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 60*x^66 + 101*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 55*x^25 + 60*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 68*x^18 + 111*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 49*x^9 + 52*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 76*x^2 + 33*x + 92, x^93 + 74*x^91 + 124*x^90 + 59*x^89 + 60*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 70*x^83 + 84*x^82 + 83*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 37*x^73 + 20*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 82*x^67 + 28*x^66 + 21*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 39*x^25 + 108*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 126*x^19 + 100*x^18 + 63*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + x^9 + 68*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 74*x^3 + 44*x^2 + 17*x + 76, x^93 + 74*x^91 + 64*x^90 + 99*x^89 + 64*x^88 + 68*x^87 + 64*x^86 + x^85 + 64*x^84 + 102*x^83 + 107*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 29*x^73 + 64*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 114*x^67 + 93*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 111*x^25 + 64*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 30*x^19 + 55*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 25*x^9 + 64*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 106*x^3 + 57*x, x^93 + 74*x^91 + 56*x^90 + 115*x^89 + 72*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 104*x^82 + 91*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 104*x^74 + 77*x^73 + 24*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 120*x^66 + 45*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 63*x^25 + 104*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 8*x^18 + 103*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 72*x^10 + 9*x^9 + 56*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 24*x^2 + 73*x + 40, x^93 + 74*x^91 + 120*x^90 + 99*x^89 + 88*x^88 + 68*x^87 + 80*x^86 + x^85 + 80*x^84 + 102*x^83 + 40*x^82 + 107*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 29*x^73 + 72*x^72 + 116*x^71 + 16*x^70 + 7*x^69 + 16*x^68 + 114*x^67 + 56*x^66 + 93*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 111*x^25 + 56*x^24 + 116*x^23 + 16*x^22 + 37*x^21 + 16*x^20 + 30*x^19 + 72*x^18 + 55*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 25*x^9 + 40*x^8 + 68*x^7 + 80*x^6 + 27*x^5 + 80*x^4 + 106*x^3 + 88*x^2 + 57*x + 120, x^93 + 74*x^91 + 52*x^90 + 43*x^89 + 100*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 60*x^82 + 99*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 117*x^73 + 76*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 20*x^66 + 69*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 87*x^25 + 52*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 108*x^18 + 15*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 17*x^9 + 28*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 68*x^2 + x + 84, x^93 + 74*x^91 + 120*x^90 + 35*x^89 + 56*x^88 + 4*x^87 + 16*x^86 + 65*x^85 + 80*x^84 + 38*x^83 + 104*x^82 + 107*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 93*x^73 + 104*x^72 + 52*x^71 + 80*x^70 + 71*x^69 + 16*x^68 + 50*x^67 + 120*x^66 + 93*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 62*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 46*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 58*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 26*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 47*x^25 + 24*x^24 + 52*x^23 + 80*x^22 + 101*x^21 + 16*x^20 + 94*x^19 + 8*x^18 + 55*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 89*x^9 + 72*x^8 + 4*x^7 + 16*x^6 + 91*x^5 + 80*x^4 + 42*x^3 + 24*x^2 + 57*x + 24, x^93 + 74*x^91 + 40*x^90 + 35*x^89 + 72*x^88 + 4*x^87 + 48*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 120*x^82 + 107*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 93*x^73 + 24*x^72 + 52*x^71 + 112*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 40*x^66 + 93*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 47*x^25 + 104*x^24 + 52*x^23 + 112*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 88*x^18 + 55*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 89*x^9 + 56*x^8 + 4*x^7 + 48*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 8*x^2 + 57*x + 104, x^93 + 74*x^91 + 4*x^90 + 107*x^89 + 84*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 108*x^82 + 99*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 53*x^73 + 28*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 36*x^66 + 69*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 23*x^25 + 100*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 92*x^18 + 15*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 81*x^9 + 44*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 20*x^2 + x + 68, x^93 + 74*x^91 + 60*x^90 + 91*x^89 + 60*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 84*x^82 + 115*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 5*x^73 + 20*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 28*x^66 + 117*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 71*x^25 + 108*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 100*x^18 + 95*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 97*x^9 + 68*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 44*x^2 + 113*x + 12, x^93 + 74*x^91 + 8*x^90 + 115*x^89 + 56*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 24*x^82 + 27*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 77*x^73 + 104*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 8*x^66 + 109*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 63*x^25 + 24*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 120*x^18 + 39*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 9*x^9 + 72*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 104*x^2 + 9*x + 24, x^93 + 74*x^91 + 100*x^90 + 59*x^89 + 36*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 6*x^83 + 12*x^82 + 19*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 37*x^73 + 12*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 18*x^67 + 4*x^66 + 85*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 39*x^25 + 116*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 62*x^19 + 124*x^18 + 127*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + x^9 + 92*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 10*x^3 + 116*x^2 + 81*x + 84, x^93 + 74*x^91 + 88*x^90 + 83*x^89 + 8*x^88 + 4*x^87 + 16*x^86 + 97*x^85 + 112*x^84 + 38*x^83 + 72*x^82 + 123*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 109*x^73 + 88*x^72 + 52*x^71 + 80*x^70 + 103*x^69 + 48*x^68 + 50*x^67 + 24*x^66 + 13*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 31*x^25 + 40*x^24 + 52*x^23 + 80*x^22 + 5*x^21 + 48*x^20 + 94*x^19 + 104*x^18 + 7*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 41*x^9 + 120*x^8 + 4*x^7 + 16*x^6 + 123*x^5 + 112*x^4 + 42*x^3 + 56*x^2 + 41*x + 104, x^93 + 74*x^91 + 64*x^90 + 99*x^89 + 32*x^88 + 4*x^87 + 65*x^85 + 64*x^84 + 38*x^83 + 64*x^82 + 43*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 29*x^73 + 96*x^72 + 52*x^71 + 71*x^69 + 64*x^68 + 50*x^67 + 64*x^66 + 29*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 111*x^25 + 32*x^24 + 52*x^23 + 101*x^21 + 64*x^20 + 94*x^19 + 64*x^18 + 119*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 25*x^9 + 96*x^8 + 4*x^7 + 91*x^5 + 64*x^4 + 42*x^3 + 64*x^2 + 121*x + 32, x^93 + 74*x^91 + 84*x^90 + 107*x^89 + 100*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 70*x^83 + 92*x^82 + 99*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 53*x^73 + 76*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 82*x^67 + 116*x^66 + 69*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 23*x^25 + 52*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 126*x^19 + 12*x^18 + 15*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 81*x^9 + 28*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 74*x^3 + 36*x^2 + x + 20, x^93 + 74*x^91 + 60*x^90 + 43*x^89 + 108*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 20*x^82 + 99*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 117*x^73 + 36*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 92*x^66 + 69*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 87*x^25 + 92*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 36*x^18 + 15*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 17*x^9 + 20*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 108*x^2 + x + 60, x^93 + 74*x^91 + 96*x^90 + 67*x^89 + 68*x^87 + 65*x^85 + 64*x^84 + 102*x^83 + 96*x^82 + 11*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 61*x^73 + 116*x^71 + 71*x^69 + 64*x^68 + 114*x^67 + 32*x^66 + 61*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 79*x^25 + 116*x^23 + 101*x^21 + 64*x^20 + 30*x^19 + 96*x^18 + 87*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 57*x^9 + 68*x^7 + 91*x^5 + 64*x^4 + 106*x^3 + 32*x^2 + 25*x + 64, x^93 + 74*x^91 + 96*x^90 + 115*x^89 + 112*x^88 + 4*x^87 + 33*x^85 + 96*x^84 + 38*x^83 + 96*x^82 + 91*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 77*x^73 + 80*x^72 + 52*x^71 + 39*x^69 + 96*x^68 + 50*x^67 + 32*x^66 + 45*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 63*x^25 + 48*x^24 + 52*x^23 + 69*x^21 + 96*x^20 + 94*x^19 + 96*x^18 + 103*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 9*x^9 + 16*x^8 + 4*x^7 + 59*x^5 + 96*x^4 + 42*x^3 + 32*x^2 + 73*x + 112, x^93 + 74*x^91 + 72*x^90 + 99*x^89 + 104*x^88 + 68*x^87 + 48*x^86 + x^85 + 48*x^84 + 102*x^83 + 24*x^82 + 107*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 29*x^73 + 120*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 8*x^66 + 93*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 111*x^25 + 8*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 120*x^18 + 55*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 25*x^9 + 24*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 104*x^2 + 57*x + 72, x^93 + 74*x^91 + 60*x^90 + 27*x^89 + 124*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 6*x^83 + 84*x^82 + 51*x^81 + 116*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 69*x^73 + 84*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 18*x^67 + 28*x^66 + 53*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 7*x^25 + 44*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 62*x^19 + 100*x^18 + 31*x^17 + 4*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 33*x^9 + 4*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 10*x^3 + 44*x^2 + 49*x + 76, x^93 + 74*x^91 + 48*x^90 + 99*x^89 + 48*x^88 + 68*x^87 + 96*x^86 + x^85 + 96*x^84 + 102*x^83 + 80*x^82 + 107*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 29*x^73 + 16*x^72 + 116*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 114*x^67 + 112*x^66 + 93*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 111*x^25 + 112*x^24 + 116*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 30*x^19 + 16*x^18 + 55*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 25*x^9 + 80*x^8 + 68*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 106*x^3 + 48*x^2 + 57*x + 48, x^93 + 74*x^91 + 124*x^90 + 107*x^89 + 108*x^88 + 100*x^87 + 104*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 84*x^82 + 35*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 53*x^73 + 36*x^72 + 20*x^71 + 8*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 28*x^66 + 5*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 23*x^25 + 92*x^24 + 20*x^23 + 72*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 100*x^18 + 79*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 81*x^9 + 20*x^8 + 100*x^7 + 40*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 44*x^2 + 65*x + 60, x^93 + 74*x^91 + 76*x^90 + 123*x^89 + 76*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 40*x^84 + 6*x^83 + 4*x^82 + 83*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 101*x^73 + 68*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 72*x^68 + 18*x^67 + 44*x^66 + 21*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 103*x^25 + 60*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 8*x^20 + 62*x^19 + 84*x^18 + 63*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + 65*x^9 + 52*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 104*x^4 + 10*x^3 + 124*x^2 + 17*x + 92, x^93 + 74*x^91 + 84*x^90 + 123*x^89 + 20*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 70*x^83 + 28*x^82 + 19*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 101*x^73 + 92*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 82*x^67 + 52*x^66 + 85*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 103*x^25 + 36*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 126*x^19 + 76*x^18 + 127*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 65*x^9 + 108*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 74*x^3 + 100*x^2 + 81*x + 68, x^93 + 74*x^91 + 8*x^90 + 3*x^89 + 8*x^88 + 68*x^87 + 48*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 88*x^82 + 75*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 125*x^73 + 88*x^72 + 116*x^71 + 112*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 72*x^66 + 125*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 15*x^25 + 40*x^24 + 116*x^23 + 112*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 56*x^18 + 23*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 121*x^9 + 120*x^8 + 68*x^7 + 48*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 40*x^2 + 89*x + 104, x^93 + 74*x^91 + 4*x^90 + 43*x^89 + 84*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 70*x^83 + 108*x^82 + 35*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 108*x^74 + 117*x^73 + 28*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 82*x^67 + 36*x^66 + 5*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 87*x^25 + 100*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 126*x^19 + 92*x^18 + 79*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 60*x^10 + 17*x^9 + 44*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 74*x^3 + 20*x^2 + 65*x + 68, x^93 + 74*x^91 + 36*x^90 + 43*x^89 + 116*x^88 + 36*x^87 + 24*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 76*x^82 + 35*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 117*x^73 + 124*x^72 + 84*x^71 + 120*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 68*x^66 + 5*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 87*x^25 + 4*x^24 + 84*x^23 + 56*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 60*x^18 + 79*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 17*x^9 + 12*x^8 + 36*x^7 + 88*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 52*x^2 + 65*x + 100, x^93 + 74*x^91 + 52*x^90 + 75*x^89 + 4*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 124*x^82 + 3*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 85*x^73 + 44*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 84*x^66 + 37*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 119*x^25 + 84*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 44*x^18 + 47*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 113*x^9 + 124*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 4*x^2 + 97*x + 52, x^93 + 74*x^91 + 48*x^90 + 19*x^89 + 4*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 80*x^82 + 59*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 45*x^73 + 52*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 112*x^66 + 77*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 95*x^25 + 52*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 16*x^18 + 71*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 105*x^9 + 4*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 48*x^2 + 105*x + 64, x^93 + 74*x^91 + 52*x^90 + 91*x^89 + 20*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 60*x^82 + 51*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 5*x^73 + 92*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 20*x^66 + 53*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 71*x^25 + 36*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 108*x^18 + 31*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 97*x^9 + 108*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 68*x^2 + 49*x + 68, x^93 + 74*x^91 + 12*x^90 + 11*x^89 + 60*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 6*x^83 + 4*x^82 + 3*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 21*x^73 + 20*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 18*x^67 + 44*x^66 + 37*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 55*x^25 + 108*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 62*x^19 + 84*x^18 + 47*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 49*x^9 + 68*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 10*x^3 + 124*x^2 + 97*x + 76, x^93 + 74*x^91 + 84*x^90 + 91*x^89 + 116*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 24*x^84 + 70*x^83 + 28*x^82 + 51*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 5*x^73 + 124*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 120*x^68 + 82*x^67 + 52*x^66 + 53*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 71*x^25 + 4*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 56*x^20 + 126*x^19 + 76*x^18 + 31*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 97*x^9 + 12*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 88*x^4 + 74*x^3 + 100*x^2 + 49*x + 36, x^93 + 74*x^91 + 8*x^90 + 99*x^89 + 8*x^88 + 4*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 38*x^83 + 24*x^82 + 43*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 29*x^73 + 88*x^72 + 52*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 50*x^67 + 8*x^66 + 29*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 111*x^25 + 40*x^24 + 52*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 94*x^19 + 120*x^18 + 119*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 25*x^9 + 120*x^8 + 4*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 42*x^3 + 104*x^2 + 121*x + 40, x^93 + 74*x^91 + 16*x^90 + 67*x^89 + 16*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 112*x^82 + 11*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 61*x^73 + 48*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 80*x^66 + 61*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 79*x^25 + 80*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 48*x^18 + 87*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 57*x^9 + 112*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 16*x^2 + 25*x + 16, x^93 + 74*x^91 + 8*x^90 + 51*x^89 + 56*x^88 + 4*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 88*x^82 + 27*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 13*x^73 + 104*x^72 + 52*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 72*x^66 + 109*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 127*x^25 + 24*x^24 + 52*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 56*x^18 + 39*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 73*x^9 + 72*x^8 + 4*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 40*x^2 + 9*x + 88, x^93 + 74*x^91 + 84*x^90 + 11*x^89 + 100*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 28*x^82 + 3*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 21*x^73 + 76*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 52*x^66 + 37*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 55*x^25 + 52*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 76*x^18 + 47*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 49*x^9 + 28*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 100*x^2 + 97*x + 84, x^93 + 74*x^91 + 44*x^90 + 107*x^89 + 28*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 36*x^82 + 99*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 53*x^73 + 52*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 12*x^66 + 69*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 23*x^25 + 76*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 116*x^18 + 15*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 81*x^9 + 100*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 92*x^2 + x + 108, x^93 + 74*x^91 + 52*x^90 + 75*x^89 + 4*x^88 + 100*x^87 + 56*x^86 + 81*x^85 + 120*x^84 + 6*x^83 + 60*x^82 + 67*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 85*x^73 + 44*x^72 + 20*x^71 + 24*x^70 + 23*x^69 + 88*x^68 + 18*x^67 + 20*x^66 + 101*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 119*x^25 + 84*x^24 + 20*x^23 + 88*x^22 + 53*x^21 + 24*x^20 + 62*x^19 + 108*x^18 + 111*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 113*x^9 + 124*x^8 + 100*x^7 + 120*x^6 + 107*x^5 + 56*x^4 + 10*x^3 + 68*x^2 + 33*x + 116, x^93 + 74*x^91 + 96*x^90 + 3*x^89 + 64*x^88 + 4*x^87 + 64*x^86 + x^85 + 38*x^83 + 32*x^82 + 11*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 32*x^74 + 125*x^73 + 64*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 50*x^67 + 96*x^66 + 61*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 15*x^25 + 64*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 94*x^19 + 32*x^18 + 87*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 32*x^10 + 121*x^9 + 64*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 42*x^3 + 96*x^2 + 25*x + 64, x^93 + 74*x^91 + 104*x^90 + 3*x^89 + 40*x^88 + 4*x^87 + 48*x^86 + x^85 + 112*x^84 + 38*x^83 + 56*x^82 + 11*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 125*x^73 + 56*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 48*x^68 + 50*x^67 + 104*x^66 + 61*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 15*x^25 + 72*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 48*x^20 + 94*x^19 + 24*x^18 + 87*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 121*x^9 + 88*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 112*x^4 + 42*x^3 + 72*x^2 + 25*x + 72, x^93 + 74*x^91 + 88*x^90 + 51*x^89 + 40*x^88 + 68*x^87 + 80*x^86 + 97*x^85 + 112*x^84 + 102*x^83 + 8*x^82 + 91*x^81 + 56*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 13*x^73 + 56*x^72 + 116*x^71 + 16*x^70 + 103*x^69 + 48*x^68 + 114*x^67 + 88*x^66 + 45*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 127*x^25 + 72*x^24 + 116*x^23 + 16*x^22 + 5*x^21 + 48*x^20 + 30*x^19 + 40*x^18 + 103*x^17 + 24*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 73*x^9 + 88*x^8 + 68*x^7 + 80*x^6 + 123*x^5 + 112*x^4 + 106*x^3 + 120*x^2 + 73*x + 72, x^93 + 74*x^91 + 108*x^90 + 27*x^89 + 44*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 100*x^82 + 51*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 69*x^73 + 100*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 76*x^66 + 53*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 7*x^25 + 28*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 52*x^18 + 31*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 33*x^9 + 84*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 28*x^2 + 49*x + 60, x^93 + 74*x^91 + 80*x^90 + 3*x^89 + 16*x^88 + 4*x^87 + 96*x^86 + x^85 + 96*x^84 + 38*x^83 + 112*x^82 + 11*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 125*x^73 + 48*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 80*x^66 + 61*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 15*x^25 + 80*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 48*x^18 + 87*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 121*x^9 + 112*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 16*x^2 + 25*x + 80, x^93 + 74*x^91 + 64*x^90 + 35*x^89 + 4*x^87 + 65*x^85 + 38*x^83 + 64*x^82 + 107*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 93*x^73 + 52*x^71 + 71*x^69 + 50*x^67 + 64*x^66 + 93*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 47*x^25 + 52*x^23 + 101*x^21 + 94*x^19 + 64*x^18 + 55*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 89*x^9 + 4*x^7 + 91*x^5 + 42*x^3 + 64*x^2 + 57*x, x^93 + 74*x^91 + 76*x^90 + 59*x^89 + 44*x^88 + 100*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 4*x^82 + 19*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 4*x^74 + 37*x^73 + 100*x^72 + 20*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 44*x^66 + 85*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 39*x^25 + 28*x^24 + 20*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 84*x^18 + 127*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 116*x^10 + x^9 + 84*x^8 + 100*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 124*x^2 + 81*x + 60, x^93 + 74*x^91 + 32*x^90 + 3*x^89 + 32*x^88 + 4*x^87 + 64*x^86 + x^85 + 64*x^84 + 38*x^83 + 96*x^82 + 11*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 125*x^73 + 96*x^72 + 52*x^71 + 64*x^70 + 7*x^69 + 64*x^68 + 50*x^67 + 32*x^66 + 61*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 15*x^25 + 32*x^24 + 52*x^23 + 64*x^22 + 37*x^21 + 64*x^20 + 94*x^19 + 96*x^18 + 87*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 121*x^9 + 96*x^8 + 4*x^7 + 64*x^6 + 27*x^5 + 64*x^4 + 42*x^3 + 32*x^2 + 25*x + 32, x^93 + 74*x^91 + 112*x^90 + 67*x^89 + 16*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 16*x^82 + 11*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 80*x^74 + 61*x^73 + 48*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 48*x^66 + 61*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 79*x^25 + 80*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 80*x^18 + 87*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 16*x^10 + 57*x^9 + 112*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 112*x^2 + 25*x + 16, x^93 + 74*x^91 + 96*x^90 + 19*x^89 + 16*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 102*x^83 + 32*x^82 + 123*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 45*x^73 + 48*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 114*x^67 + 96*x^66 + 13*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 95*x^25 + 80*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 30*x^19 + 32*x^18 + 7*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 105*x^9 + 112*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 106*x^3 + 96*x^2 + 41*x + 80, x^93 + 74*x^91 + 51*x^89 + 48*x^88 + 68*x^87 + 97*x^85 + 32*x^84 + 102*x^83 + 91*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 13*x^73 + 16*x^72 + 116*x^71 + 103*x^69 + 32*x^68 + 114*x^67 + 45*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 127*x^25 + 112*x^24 + 116*x^23 + 5*x^21 + 32*x^20 + 30*x^19 + 103*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 73*x^9 + 80*x^8 + 68*x^7 + 123*x^5 + 32*x^4 + 106*x^3 + 73*x + 112, x^93 + 74*x^91 + 36*x^90 + 43*x^89 + 20*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 88*x^84 + 6*x^83 + 12*x^82 + 99*x^81 + 124*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 117*x^73 + 92*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 56*x^68 + 18*x^67 + 4*x^66 + 69*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 87*x^25 + 36*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 120*x^20 + 62*x^19 + 124*x^18 + 15*x^17 + 44*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 17*x^9 + 108*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 24*x^4 + 10*x^3 + 116*x^2 + x + 68, x^93 + 74*x^91 + 40*x^90 + 115*x^89 + 120*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 120*x^82 + 27*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 77*x^73 + 40*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 40*x^66 + 109*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 63*x^25 + 88*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 88*x^18 + 39*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 9*x^9 + 8*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 8*x^2 + 9*x + 88, x^93 + 74*x^91 + 124*x^90 + 107*x^89 + 12*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 70*x^83 + 20*x^82 + 99*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 53*x^73 + 4*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 82*x^67 + 92*x^66 + 69*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 23*x^25 + 124*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 126*x^19 + 36*x^18 + 15*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 81*x^9 + 116*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 74*x^3 + 108*x^2 + x + 28, x^93 + 74*x^91 + 116*x^90 + 43*x^89 + 36*x^88 + 100*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 6*x^83 + 124*x^82 + 99*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 117*x^73 + 12*x^72 + 20*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 18*x^67 + 84*x^66 + 69*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 87*x^25 + 116*x^24 + 20*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 62*x^19 + 44*x^18 + 15*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 17*x^9 + 92*x^8 + 100*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 10*x^3 + 4*x^2 + x + 20, x^93 + 74*x^91 + 52*x^90 + 27*x^89 + 20*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 124*x^82 + 51*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 69*x^73 + 92*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 84*x^66 + 53*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 7*x^25 + 36*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 44*x^18 + 31*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 33*x^9 + 108*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 4*x^2 + 49*x + 4, x^93 + 74*x^91 + 44*x^90 + 107*x^89 + 28*x^88 + 100*x^87 + 8*x^86 + 17*x^85 + 72*x^84 + 6*x^83 + 100*x^82 + 35*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 53*x^73 + 52*x^72 + 20*x^71 + 40*x^70 + 87*x^69 + 104*x^68 + 18*x^67 + 76*x^66 + 5*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 23*x^25 + 76*x^24 + 20*x^23 + 104*x^22 + 117*x^21 + 40*x^20 + 62*x^19 + 52*x^18 + 79*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 81*x^9 + 100*x^8 + 100*x^7 + 72*x^6 + 43*x^5 + 8*x^4 + 10*x^3 + 28*x^2 + 65*x + 44, x^93 + 74*x^91 + 28*x^90 + 107*x^89 + 12*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 104*x^84 + 6*x^83 + 52*x^82 + 35*x^81 + 100*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 53*x^73 + 4*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 8*x^68 + 18*x^67 + 60*x^66 + 5*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 23*x^25 + 124*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 72*x^20 + 62*x^19 + 68*x^18 + 79*x^17 + 52*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 81*x^9 + 116*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 40*x^4 + 10*x^3 + 76*x^2 + 65*x + 92, x^93 + 74*x^91 + 40*x^90 + 83*x^89 + 24*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 56*x^82 + 123*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 109*x^73 + 8*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 104*x^66 + 13*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 31*x^25 + 120*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 24*x^18 + 7*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 41*x^9 + 104*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 72*x^2 + 41*x + 56, x^93 + 74*x^91 + 88*x^90 + 99*x^89 + 88*x^88 + 4*x^87 + 80*x^86 + 65*x^85 + 16*x^84 + 38*x^83 + 8*x^82 + 43*x^81 + 72*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 72*x^74 + 29*x^73 + 72*x^72 + 52*x^71 + 16*x^70 + 71*x^69 + 80*x^68 + 50*x^67 + 88*x^66 + 29*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 62*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 46*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 58*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 26*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 111*x^25 + 56*x^24 + 52*x^23 + 16*x^22 + 101*x^21 + 80*x^20 + 94*x^19 + 40*x^18 + 119*x^17 + 104*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 40*x^10 + 25*x^9 + 40*x^8 + 4*x^7 + 80*x^6 + 91*x^5 + 16*x^4 + 42*x^3 + 120*x^2 + 121*x + 56, x^93 + 74*x^91 + 84*x^90 + 75*x^89 + 36*x^88 + 100*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 6*x^83 + 28*x^82 + 67*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 85*x^73 + 12*x^72 + 20*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 18*x^67 + 52*x^66 + 101*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 119*x^25 + 116*x^24 + 20*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 62*x^19 + 76*x^18 + 111*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 113*x^9 + 92*x^8 + 100*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 10*x^3 + 100*x^2 + 33*x + 20, x^93 + 74*x^91 + 99*x^89 + 32*x^88 + 68*x^87 + 64*x^86 + x^85 + 102*x^83 + 64*x^82 + 107*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 29*x^73 + 96*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 114*x^67 + 64*x^66 + 93*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 111*x^25 + 32*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 30*x^19 + 64*x^18 + 55*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 25*x^9 + 96*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 106*x^3 + 64*x^2 + 57*x + 96, x^93 + 74*x^91 + 8*x^90 + 35*x^89 + 40*x^88 + 68*x^87 + 48*x^86 + x^85 + 48*x^84 + 102*x^83 + 88*x^82 + 43*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 93*x^73 + 56*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 72*x^66 + 29*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 47*x^25 + 72*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 56*x^18 + 119*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 89*x^9 + 88*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 40*x^2 + 121*x + 8, x^93 + 74*x^91 + 124*x^90 + 27*x^89 + 92*x^88 + 100*x^87 + 40*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 20*x^82 + 51*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 69*x^73 + 116*x^72 + 20*x^71 + 72*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 92*x^66 + 53*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 7*x^25 + 12*x^24 + 20*x^23 + 8*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 36*x^18 + 31*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + 33*x^9 + 36*x^8 + 100*x^7 + 104*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 108*x^2 + 49*x + 44, x^93 + 74*x^91 + 40*x^90 + 83*x^89 + 24*x^88 + 68*x^87 + 48*x^86 + 33*x^85 + 16*x^84 + 102*x^83 + 120*x^82 + 59*x^81 + 8*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 109*x^73 + 8*x^72 + 116*x^71 + 112*x^70 + 39*x^69 + 80*x^68 + 114*x^67 + 40*x^66 + 77*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 31*x^25 + 120*x^24 + 116*x^23 + 112*x^22 + 69*x^21 + 80*x^20 + 30*x^19 + 88*x^18 + 71*x^17 + 40*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 41*x^9 + 104*x^8 + 68*x^7 + 48*x^6 + 59*x^5 + 16*x^4 + 106*x^3 + 8*x^2 + 105*x + 120, x^93 + 74*x^91 + 88*x^90 + 19*x^89 + 104*x^88 + 68*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 102*x^83 + 8*x^82 + 123*x^81 + 120*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 72*x^74 + 45*x^73 + 120*x^72 + 116*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 114*x^67 + 88*x^66 + 13*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 30*x^57 + 16*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 78*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 90*x^41 + 112*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 122*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 56*x^26 + 95*x^25 + 8*x^24 + 116*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 30*x^19 + 40*x^18 + 7*x^17 + 88*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 40*x^10 + 105*x^9 + 24*x^8 + 68*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 106*x^3 + 120*x^2 + 41*x + 8, x^93 + 74*x^91 + 28*x^90 + 43*x^89 + 108*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 52*x^82 + 99*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 117*x^73 + 36*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 60*x^66 + 69*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 87*x^25 + 92*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 68*x^18 + 15*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 17*x^9 + 20*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 76*x^2 + x + 60, x^93 + 74*x^91 + 56*x^90 + 67*x^89 + 24*x^88 + 4*x^87 + 16*x^86 + x^85 + 16*x^84 + 38*x^83 + 40*x^82 + 75*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 104*x^74 + 61*x^73 + 8*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 56*x^66 + 125*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 24*x^26 + 79*x^25 + 120*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 72*x^18 + 23*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 72*x^10 + 57*x^9 + 104*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 88*x^2 + 89*x + 120, x^93 + 74*x^91 + 40*x^90 + 67*x^89 + 40*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 48*x^84 + 102*x^83 + 56*x^82 + 11*x^81 + 120*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 61*x^73 + 56*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 112*x^68 + 114*x^67 + 104*x^66 + 61*x^65 + 40*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 79*x^25 + 72*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 112*x^20 + 30*x^19 + 24*x^18 + 87*x^17 + 88*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 57*x^9 + 88*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 48*x^4 + 106*x^3 + 72*x^2 + 25*x + 8, x^93 + 74*x^91 + 12*x^90 + 91*x^89 + 12*x^88 + 36*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 4*x^82 + 51*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 5*x^73 + 4*x^72 + 84*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 44*x^66 + 53*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 71*x^25 + 124*x^24 + 84*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 84*x^18 + 31*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 97*x^9 + 116*x^8 + 36*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 124*x^2 + 49*x + 92, x^93 + 74*x^91 + 84*x^90 + 27*x^89 + 84*x^88 + 36*x^87 + 120*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 28*x^82 + 115*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 69*x^73 + 28*x^72 + 84*x^71 + 88*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 52*x^66 + 117*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 7*x^25 + 100*x^24 + 84*x^23 + 24*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 76*x^18 + 95*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 33*x^9 + 44*x^8 + 36*x^7 + 56*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 100*x^2 + 113*x + 4, x^93 + 74*x^91 + 12*x^90 + 11*x^89 + 28*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 68*x^82 + 67*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 21*x^73 + 52*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 108*x^66 + 101*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 55*x^25 + 76*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 20*x^18 + 111*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 49*x^9 + 100*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 60*x^2 + 33*x + 108, x^93 + 74*x^91 + 20*x^90 + 11*x^89 + 100*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 28*x^82 + 67*x^81 + 44*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 21*x^73 + 76*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 52*x^66 + 101*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 55*x^25 + 52*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 76*x^18 + 111*x^17 + 28*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 49*x^9 + 28*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 100*x^2 + 33*x + 20, x^93 + 74*x^91 + 28*x^90 + 59*x^89 + 28*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 116*x^82 + 19*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 37*x^73 + 52*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 124*x^66 + 85*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 39*x^25 + 76*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 4*x^18 + 127*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + x^9 + 100*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 12*x^2 + 81*x + 108, x^93 + 74*x^91 + 84*x^90 + 27*x^89 + 116*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 92*x^82 + 51*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 69*x^73 + 124*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 116*x^66 + 53*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 7*x^25 + 4*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 12*x^18 + 31*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 33*x^9 + 12*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 36*x^2 + 49*x + 100, x^93 + 74*x^91 + 100*x^90 + 107*x^89 + 52*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 76*x^82 + 35*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 53*x^73 + 60*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 68*x^66 + 5*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 23*x^25 + 68*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 60*x^18 + 79*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 81*x^9 + 76*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 52*x^2 + 65*x + 100, x^93 + 74*x^91 + 44*x^90 + 107*x^89 + 124*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 70*x^83 + 36*x^82 + 99*x^81 + 116*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 36*x^74 + 53*x^73 + 84*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 82*x^67 + 12*x^66 + 69*x^65 + 60*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 23*x^25 + 44*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 126*x^19 + 116*x^18 + 15*x^17 + 4*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 20*x^10 + 81*x^9 + 4*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 74*x^3 + 92*x^2 + x + 76, x^93 + 74*x^91 + 16*x^90 + 83*x^89 + 4*x^87 + 32*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 112*x^82 + 123*x^81 + 64*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 109*x^73 + 52*x^71 + 32*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 80*x^66 + 13*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 31*x^25 + 52*x^23 + 32*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 48*x^18 + 7*x^17 + 64*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 41*x^9 + 4*x^7 + 32*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 16*x^2 + 41*x + 64, x^93 + 74*x^91 + 80*x^90 + 35*x^89 + 48*x^88 + 4*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 38*x^83 + 112*x^82 + 107*x^81 + 16*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 93*x^73 + 16*x^72 + 52*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 50*x^67 + 80*x^66 + 93*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 62*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 46*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 58*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 26*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 47*x^25 + 112*x^24 + 52*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 94*x^19 + 48*x^18 + 55*x^17 + 80*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 89*x^9 + 80*x^8 + 4*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 42*x^3 + 16*x^2 + 57*x + 112, x^93 + 74*x^91 + 28*x^90 + 75*x^89 + 108*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 116*x^82 + 3*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 85*x^73 + 36*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 124*x^66 + 37*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 119*x^25 + 92*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 4*x^18 + 47*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 113*x^9 + 20*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 12*x^2 + 97*x + 124, x^93 + 74*x^91 + 52*x^90 + 75*x^89 + 68*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 124*x^82 + 3*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 124*x^74 + 85*x^73 + 108*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 84*x^66 + 37*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 119*x^25 + 20*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 44*x^18 + 47*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 12*x^10 + 113*x^9 + 60*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 4*x^2 + 97*x + 116, x^93 + 74*x^91 + 104*x^90 + 19*x^89 + 120*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 16*x^84 + 38*x^83 + 120*x^82 + 59*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 45*x^73 + 40*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 80*x^68 + 50*x^67 + 40*x^66 + 77*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 95*x^25 + 88*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 80*x^20 + 94*x^19 + 88*x^18 + 71*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 105*x^9 + 8*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 16*x^4 + 42*x^3 + 8*x^2 + 105*x + 24, x^93 + 74*x^91 + 76*x^90 + 11*x^89 + 92*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 68*x^82 + 3*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 21*x^73 + 116*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 108*x^66 + 37*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 55*x^25 + 12*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 20*x^18 + 47*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 49*x^9 + 36*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 60*x^2 + 97*x + 108, x^93 + 74*x^91 + 40*x^90 + 3*x^89 + 8*x^88 + 4*x^87 + 48*x^86 + x^85 + 48*x^84 + 38*x^83 + 120*x^82 + 11*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 125*x^73 + 88*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 40*x^66 + 61*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 15*x^25 + 40*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 88*x^18 + 87*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 121*x^9 + 120*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 8*x^2 + 25*x + 40, x^93 + 74*x^91 + 92*x^90 + 11*x^89 + 44*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 52*x^82 + 67*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 52*x^74 + 21*x^73 + 100*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 60*x^66 + 101*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 55*x^25 + 28*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 68*x^18 + 111*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 100*x^10 + 49*x^9 + 84*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 76*x^2 + 33*x + 60, x^93 + 74*x^91 + 80*x^90 + 3*x^89 + 80*x^88 + 4*x^87 + 96*x^86 + x^85 + 96*x^84 + 38*x^83 + 112*x^82 + 11*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 112*x^74 + 125*x^73 + 112*x^72 + 52*x^71 + 96*x^70 + 7*x^69 + 96*x^68 + 50*x^67 + 80*x^66 + 61*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 16*x^26 + 15*x^25 + 16*x^24 + 52*x^23 + 96*x^22 + 37*x^21 + 96*x^20 + 94*x^19 + 48*x^18 + 87*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 48*x^10 + 121*x^9 + 48*x^8 + 4*x^7 + 96*x^6 + 27*x^5 + 96*x^4 + 42*x^3 + 16*x^2 + 25*x + 16, x^93 + 74*x^91 + 115*x^89 + 16*x^88 + 68*x^87 + 97*x^85 + 96*x^84 + 102*x^83 + 27*x^81 + 48*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 77*x^73 + 48*x^72 + 116*x^71 + 103*x^69 + 96*x^68 + 114*x^67 + 109*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 63*x^25 + 80*x^24 + 116*x^23 + 5*x^21 + 96*x^20 + 30*x^19 + 39*x^17 + 112*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 9*x^9 + 112*x^8 + 68*x^7 + 123*x^5 + 96*x^4 + 106*x^3 + 9*x + 80, x^93 + 74*x^91 + 60*x^90 + 75*x^89 + 76*x^88 + 100*x^87 + 104*x^86 + 81*x^85 + 104*x^84 + 6*x^83 + 20*x^82 + 67*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 85*x^73 + 68*x^72 + 20*x^71 + 8*x^70 + 23*x^69 + 8*x^68 + 18*x^67 + 92*x^66 + 101*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 119*x^25 + 60*x^24 + 20*x^23 + 72*x^22 + 53*x^21 + 72*x^20 + 62*x^19 + 36*x^18 + 111*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 113*x^9 + 52*x^8 + 100*x^7 + 40*x^6 + 107*x^5 + 40*x^4 + 10*x^3 + 108*x^2 + 33*x + 28, x^93 + 74*x^91 + 16*x^90 + 51*x^89 + 64*x^88 + 4*x^87 + 32*x^86 + 33*x^85 + 64*x^84 + 38*x^83 + 112*x^82 + 27*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 13*x^73 + 64*x^72 + 52*x^71 + 32*x^70 + 39*x^69 + 64*x^68 + 50*x^67 + 80*x^66 + 109*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 94*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 14*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 26*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 58*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 127*x^25 + 64*x^24 + 52*x^23 + 32*x^22 + 69*x^21 + 64*x^20 + 94*x^19 + 48*x^18 + 39*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 73*x^9 + 64*x^8 + 4*x^7 + 32*x^6 + 59*x^5 + 64*x^4 + 42*x^3 + 16*x^2 + 9*x, x^93 + 74*x^91 + 124*x^90 + 43*x^89 + 108*x^88 + 36*x^87 + 40*x^86 + 81*x^85 + 104*x^84 + 70*x^83 + 20*x^82 + 35*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 20*x^74 + 117*x^73 + 36*x^72 + 84*x^71 + 72*x^70 + 23*x^69 + 8*x^68 + 82*x^67 + 92*x^66 + 5*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 87*x^25 + 92*x^24 + 84*x^23 + 8*x^22 + 53*x^21 + 72*x^20 + 126*x^19 + 36*x^18 + 79*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 68*x^10 + 17*x^9 + 20*x^8 + 36*x^7 + 104*x^6 + 107*x^5 + 40*x^4 + 74*x^3 + 108*x^2 + 65*x + 124, x^93 + 74*x^91 + 104*x^90 + 99*x^89 + 72*x^88 + 68*x^87 + 112*x^86 + x^85 + 112*x^84 + 102*x^83 + 120*x^82 + 107*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 29*x^73 + 24*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 40*x^66 + 93*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 111*x^25 + 104*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 88*x^18 + 55*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 25*x^9 + 56*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 8*x^2 + 57*x + 40, x^93 + 74*x^91 + 96*x^90 + 19*x^89 + 80*x^88 + 68*x^87 + 64*x^86 + 33*x^85 + 96*x^84 + 102*x^83 + 32*x^82 + 123*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 45*x^73 + 112*x^72 + 116*x^71 + 64*x^70 + 39*x^69 + 96*x^68 + 114*x^67 + 96*x^66 + 13*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 30*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 78*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 90*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 122*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 95*x^25 + 16*x^24 + 116*x^23 + 64*x^22 + 69*x^21 + 96*x^20 + 30*x^19 + 32*x^18 + 7*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 105*x^9 + 48*x^8 + 68*x^7 + 64*x^6 + 59*x^5 + 96*x^4 + 106*x^3 + 96*x^2 + 41*x + 16, x^93 + 74*x^91 + 24*x^90 + 67*x^89 + 24*x^88 + 4*x^87 + 80*x^86 + x^85 + 16*x^84 + 38*x^83 + 72*x^82 + 75*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 61*x^73 + 8*x^72 + 52*x^71 + 16*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 24*x^66 + 125*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 79*x^25 + 120*x^24 + 52*x^23 + 16*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 104*x^18 + 23*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 57*x^9 + 104*x^8 + 4*x^7 + 80*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 56*x^2 + 89*x + 120, x^93 + 74*x^91 + 116*x^90 + 123*x^89 + 116*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 124*x^82 + 19*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 60*x^74 + 101*x^73 + 124*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 84*x^66 + 85*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 103*x^25 + 4*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 44*x^18 + 127*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 76*x^10 + 65*x^9 + 12*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 4*x^2 + 81*x + 36, x^93 + 74*x^91 + 52*x^90 + 91*x^89 + 52*x^88 + 100*x^87 + 120*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 124*x^82 + 115*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 5*x^73 + 60*x^72 + 20*x^71 + 88*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 84*x^66 + 117*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 71*x^25 + 68*x^24 + 20*x^23 + 24*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 44*x^18 + 95*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 97*x^9 + 76*x^8 + 100*x^7 + 56*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 4*x^2 + 113*x + 36, x^93 + 74*x^91 + 124*x^90 + 59*x^89 + 28*x^88 + 36*x^87 + 104*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 84*x^82 + 83*x^81 + 20*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 37*x^73 + 52*x^72 + 84*x^71 + 8*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 28*x^66 + 21*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 39*x^25 + 76*x^24 + 84*x^23 + 72*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 100*x^18 + 63*x^17 + 36*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + x^9 + 100*x^8 + 36*x^7 + 40*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 44*x^2 + 17*x + 44, x^93 + 74*x^91 + 112*x^90 + 115*x^89 + 96*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 38*x^83 + 16*x^82 + 91*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 77*x^73 + 32*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 50*x^67 + 48*x^66 + 45*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 63*x^25 + 96*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 94*x^19 + 80*x^18 + 103*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 9*x^9 + 32*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 42*x^3 + 112*x^2 + 73*x + 32, x^93 + 74*x^91 + 40*x^90 + 67*x^89 + 72*x^88 + 4*x^87 + 48*x^86 + x^85 + 48*x^84 + 38*x^83 + 120*x^82 + 75*x^81 + 24*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 61*x^73 + 24*x^72 + 52*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 40*x^66 + 125*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 79*x^25 + 104*x^24 + 52*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 88*x^18 + 23*x^17 + 120*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 57*x^9 + 56*x^8 + 4*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 8*x^2 + 89*x + 104, x^93 + 74*x^91 + 104*x^90 + 115*x^89 + 56*x^88 + 68*x^87 + 48*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 56*x^82 + 27*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 77*x^73 + 104*x^72 + 116*x^71 + 112*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 104*x^66 + 109*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 63*x^25 + 24*x^24 + 116*x^23 + 112*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 24*x^18 + 39*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 9*x^9 + 72*x^8 + 68*x^7 + 48*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 72*x^2 + 9*x + 24, x^93 + 74*x^91 + 28*x^90 + 43*x^89 + 44*x^88 + 100*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 6*x^83 + 52*x^82 + 99*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 117*x^73 + 100*x^72 + 20*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 18*x^67 + 60*x^66 + 69*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 14*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 94*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 106*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 106*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 87*x^25 + 28*x^24 + 20*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 62*x^19 + 68*x^18 + 15*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 17*x^9 + 84*x^8 + 100*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 10*x^3 + 76*x^2 + x + 124, x^93 + 74*x^91 + 100*x^90 + 91*x^89 + 100*x^88 + 36*x^87 + 88*x^86 + 113*x^85 + 56*x^84 + 70*x^83 + 76*x^82 + 51*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 5*x^73 + 76*x^72 + 84*x^71 + 56*x^70 + 55*x^69 + 24*x^68 + 82*x^67 + 68*x^66 + 53*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 71*x^25 + 52*x^24 + 84*x^23 + 120*x^22 + 85*x^21 + 88*x^20 + 126*x^19 + 60*x^18 + 31*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 97*x^9 + 28*x^8 + 36*x^7 + 24*x^6 + 11*x^5 + 120*x^4 + 74*x^3 + 52*x^2 + 49*x + 84, x^93 + 74*x^91 + 28*x^90 + 75*x^89 + 44*x^88 + 100*x^87 + 40*x^86 + 81*x^85 + 40*x^84 + 6*x^83 + 52*x^82 + 67*x^81 + 68*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 85*x^73 + 100*x^72 + 20*x^71 + 72*x^70 + 23*x^69 + 72*x^68 + 18*x^67 + 60*x^66 + 101*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 119*x^25 + 28*x^24 + 20*x^23 + 8*x^22 + 53*x^21 + 8*x^20 + 62*x^19 + 68*x^18 + 111*x^17 + 20*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 113*x^9 + 84*x^8 + 100*x^7 + 104*x^6 + 107*x^5 + 104*x^4 + 10*x^3 + 76*x^2 + 33*x + 124, x^93 + 74*x^91 + 60*x^90 + 123*x^89 + 60*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 84*x^82 + 83*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 84*x^74 + 101*x^73 + 20*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 28*x^66 + 21*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 103*x^25 + 108*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 100*x^18 + 63*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 4*x^10 + 65*x^9 + 68*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 44*x^2 + 17*x + 12, x^93 + 74*x^91 + 44*x^90 + 91*x^89 + 12*x^88 + 36*x^87 + 8*x^86 + 113*x^85 + 104*x^84 + 70*x^83 + 100*x^82 + 51*x^81 + 100*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 5*x^73 + 4*x^72 + 84*x^71 + 40*x^70 + 55*x^69 + 8*x^68 + 82*x^67 + 76*x^66 + 53*x^65 + 12*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 71*x^25 + 124*x^24 + 84*x^23 + 104*x^22 + 85*x^21 + 72*x^20 + 126*x^19 + 52*x^18 + 31*x^17 + 52*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 97*x^9 + 116*x^8 + 36*x^7 + 72*x^6 + 11*x^5 + 40*x^4 + 74*x^3 + 28*x^2 + 49*x + 92, x^93 + 74*x^91 + 36*x^90 + 123*x^89 + 68*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 76*x^82 + 83*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 76*x^74 + 101*x^73 + 108*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 68*x^66 + 21*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 103*x^25 + 20*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 60*x^18 + 63*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 28*x^10 + 65*x^9 + 60*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 52*x^2 + 17*x + 116, x^93 + 74*x^91 + 96*x^90 + 51*x^89 + 112*x^88 + 4*x^87 + 33*x^85 + 96*x^84 + 38*x^83 + 96*x^82 + 27*x^81 + 16*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 32*x^74 + 13*x^73 + 80*x^72 + 52*x^71 + 39*x^69 + 96*x^68 + 50*x^67 + 32*x^66 + 109*x^65 + 48*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 94*x^57 + 96*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 64*x^50 + 14*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 26*x^41 + 32*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 64*x^34 + 58*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 96*x^26 + 127*x^25 + 48*x^24 + 52*x^23 + 69*x^21 + 96*x^20 + 94*x^19 + 96*x^18 + 39*x^17 + 80*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 32*x^10 + 73*x^9 + 16*x^8 + 4*x^7 + 59*x^5 + 96*x^4 + 42*x^3 + 32*x^2 + 9*x + 112, x^93 + 74*x^91 + 36*x^90 + 43*x^89 + 116*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 12*x^82 + 99*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 76*x^74 + 117*x^73 + 124*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 4*x^66 + 69*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 116*x^26 + 87*x^25 + 4*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 124*x^18 + 15*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 28*x^10 + 17*x^9 + 12*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 116*x^2 + x + 36, x^93 + 74*x^91 + 8*x^90 + 35*x^89 + 104*x^88 + 68*x^87 + 48*x^86 + x^85 + 48*x^84 + 102*x^83 + 88*x^82 + 43*x^81 + 56*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 88*x^74 + 93*x^73 + 120*x^72 + 116*x^71 + 112*x^70 + 7*x^69 + 112*x^68 + 114*x^67 + 72*x^66 + 29*x^65 + 104*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 62*x^57 + 16*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 46*x^49 + 48*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 58*x^41 + 112*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 26*x^33 + 80*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 47*x^25 + 8*x^24 + 116*x^23 + 112*x^22 + 37*x^21 + 112*x^20 + 30*x^19 + 56*x^18 + 119*x^17 + 24*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 120*x^10 + 89*x^9 + 24*x^8 + 68*x^7 + 48*x^6 + 27*x^5 + 48*x^4 + 106*x^3 + 40*x^2 + 121*x + 72, x^93 + 74*x^91 + 108*x^90 + 107*x^89 + 92*x^88 + 36*x^87 + 72*x^86 + 81*x^85 + 8*x^84 + 70*x^83 + 100*x^82 + 99*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 53*x^73 + 116*x^72 + 84*x^71 + 104*x^70 + 23*x^69 + 40*x^68 + 82*x^67 + 76*x^66 + 69*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 14*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 94*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 106*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 106*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 23*x^25 + 12*x^24 + 84*x^23 + 40*x^22 + 53*x^21 + 104*x^20 + 126*x^19 + 52*x^18 + 15*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 81*x^9 + 36*x^8 + 36*x^7 + 8*x^6 + 107*x^5 + 72*x^4 + 74*x^3 + 28*x^2 + x + 44, x^93 + 74*x^91 + 3*x^89 + 32*x^88 + 4*x^87 + x^85 + 64*x^84 + 38*x^83 + 11*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 125*x^73 + 96*x^72 + 52*x^71 + 7*x^69 + 64*x^68 + 50*x^67 + 61*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 15*x^25 + 32*x^24 + 52*x^23 + 37*x^21 + 64*x^20 + 94*x^19 + 87*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 121*x^9 + 96*x^8 + 4*x^7 + 27*x^5 + 64*x^4 + 42*x^3 + 25*x + 32, x^93 + 74*x^91 + 52*x^90 + 59*x^89 + 116*x^88 + 36*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 60*x^82 + 83*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 37*x^73 + 124*x^72 + 84*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 20*x^66 + 21*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 39*x^25 + 4*x^24 + 84*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 108*x^18 + 63*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + x^9 + 12*x^8 + 36*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 68*x^2 + 17*x + 36, x^93 + 74*x^91 + 100*x^90 + 123*x^89 + 68*x^88 + 100*x^87 + 24*x^86 + 113*x^85 + 56*x^84 + 6*x^83 + 12*x^82 + 83*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 101*x^73 + 108*x^72 + 20*x^71 + 120*x^70 + 55*x^69 + 24*x^68 + 18*x^67 + 4*x^66 + 21*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 103*x^25 + 20*x^24 + 20*x^23 + 56*x^22 + 85*x^21 + 88*x^20 + 62*x^19 + 124*x^18 + 63*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 65*x^9 + 60*x^8 + 100*x^7 + 88*x^6 + 11*x^5 + 120*x^4 + 10*x^3 + 116*x^2 + 17*x + 116, x^93 + 74*x^91 + 28*x^90 + 11*x^89 + 44*x^88 + 36*x^87 + 104*x^86 + 17*x^85 + 104*x^84 + 70*x^83 + 116*x^82 + 67*x^81 + 4*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 116*x^74 + 21*x^73 + 100*x^72 + 84*x^71 + 8*x^70 + 87*x^69 + 8*x^68 + 82*x^67 + 124*x^66 + 101*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 78*x^57 + 120*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 72*x^50 + 30*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 42*x^41 + 8*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 56*x^34 + 42*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 55*x^25 + 28*x^24 + 84*x^23 + 72*x^22 + 117*x^21 + 72*x^20 + 126*x^19 + 4*x^18 + 111*x^17 + 84*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 36*x^10 + 49*x^9 + 84*x^8 + 36*x^7 + 40*x^6 + 43*x^5 + 40*x^4 + 74*x^3 + 12*x^2 + 33*x + 60, x^93 + 74*x^91 + 16*x^90 + 83*x^89 + 96*x^88 + 4*x^87 + 32*x^86 + 97*x^85 + 38*x^83 + 112*x^82 + 123*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 48*x^74 + 109*x^73 + 32*x^72 + 52*x^71 + 32*x^70 + 103*x^69 + 50*x^67 + 80*x^66 + 13*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 30*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 96*x^50 + 78*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 90*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 32*x^34 + 122*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 31*x^25 + 96*x^24 + 52*x^23 + 32*x^22 + 5*x^21 + 94*x^19 + 48*x^18 + 7*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 112*x^10 + 41*x^9 + 32*x^8 + 4*x^7 + 32*x^6 + 123*x^5 + 42*x^3 + 16*x^2 + 41*x + 32, x^93 + 74*x^91 + 116*x^90 + 11*x^89 + 36*x^88 + 36*x^87 + 120*x^86 + 17*x^85 + 120*x^84 + 70*x^83 + 60*x^82 + 67*x^81 + 108*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 21*x^73 + 12*x^72 + 84*x^71 + 88*x^70 + 87*x^69 + 88*x^68 + 82*x^67 + 20*x^66 + 101*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 78*x^57 + 40*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 30*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 42*x^41 + 88*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 42*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 55*x^25 + 116*x^24 + 84*x^23 + 24*x^22 + 117*x^21 + 24*x^20 + 126*x^19 + 108*x^18 + 111*x^17 + 92*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 49*x^9 + 92*x^8 + 36*x^7 + 56*x^6 + 43*x^5 + 56*x^4 + 74*x^3 + 68*x^2 + 33*x + 84, x^93 + 74*x^91 + 104*x^90 + 35*x^89 + 72*x^88 + 68*x^87 + 112*x^86 + x^85 + 112*x^84 + 102*x^83 + 120*x^82 + 43*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 120*x^74 + 93*x^73 + 24*x^72 + 116*x^71 + 48*x^70 + 7*x^69 + 48*x^68 + 114*x^67 + 40*x^66 + 29*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 62*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 46*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 58*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 26*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 47*x^25 + 104*x^24 + 116*x^23 + 48*x^22 + 37*x^21 + 48*x^20 + 30*x^19 + 88*x^18 + 119*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 24*x^10 + 89*x^9 + 56*x^8 + 68*x^7 + 112*x^6 + 27*x^5 + 112*x^4 + 106*x^3 + 8*x^2 + 121*x + 40, x^93 + 74*x^91 + 52*x^90 + 91*x^89 + 84*x^88 + 36*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 70*x^83 + 60*x^82 + 51*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 124*x^74 + 5*x^73 + 28*x^72 + 84*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 82*x^67 + 20*x^66 + 53*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 24*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 104*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 68*x^26 + 71*x^25 + 100*x^24 + 84*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 126*x^19 + 108*x^18 + 31*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 12*x^10 + 97*x^9 + 44*x^8 + 36*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 74*x^3 + 68*x^2 + 49*x + 4, x^93 + 74*x^91 + 84*x^90 + 91*x^89 + 20*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 24*x^84 + 6*x^83 + 92*x^82 + 115*x^81 + 60*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 5*x^73 + 92*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 120*x^68 + 18*x^67 + 116*x^66 + 117*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 71*x^25 + 36*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 56*x^20 + 62*x^19 + 12*x^18 + 95*x^17 + 108*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 97*x^9 + 108*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 88*x^4 + 10*x^3 + 36*x^2 + 113*x + 4, x^93 + 74*x^91 + 108*x^90 + 123*x^89 + 44*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 40*x^84 + 70*x^83 + 36*x^82 + 19*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 101*x^73 + 100*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 72*x^68 + 82*x^67 + 12*x^66 + 85*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 103*x^25 + 28*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 8*x^20 + 126*x^19 + 116*x^18 + 127*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 65*x^9 + 84*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 104*x^4 + 74*x^3 + 92*x^2 + 81*x + 124, x^93 + 74*x^91 + 20*x^90 + 59*x^89 + 84*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 24*x^84 + 6*x^83 + 28*x^82 + 19*x^81 + 124*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 37*x^73 + 28*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 120*x^68 + 18*x^67 + 52*x^66 + 85*x^65 + 20*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 8*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 120*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 39*x^25 + 100*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 56*x^20 + 62*x^19 + 76*x^18 + 127*x^17 + 44*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + x^9 + 44*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 88*x^4 + 10*x^3 + 100*x^2 + 81*x + 68, x^93 + 74*x^91 + 40*x^90 + 67*x^89 + 72*x^88 + 68*x^87 + 112*x^86 + 65*x^85 + 112*x^84 + 102*x^83 + 56*x^82 + 11*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 56*x^74 + 61*x^73 + 24*x^72 + 116*x^71 + 48*x^70 + 71*x^69 + 48*x^68 + 114*x^67 + 104*x^66 + 61*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 48*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 80*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 79*x^25 + 104*x^24 + 116*x^23 + 48*x^22 + 101*x^21 + 48*x^20 + 30*x^19 + 24*x^18 + 87*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 88*x^10 + 57*x^9 + 56*x^8 + 68*x^7 + 112*x^6 + 91*x^5 + 112*x^4 + 106*x^3 + 72*x^2 + 25*x + 40, x^93 + 74*x^91 + 48*x^90 + 19*x^89 + 68*x^87 + 32*x^86 + 33*x^85 + 102*x^83 + 16*x^82 + 123*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 45*x^73 + 116*x^71 + 32*x^70 + 39*x^69 + 114*x^67 + 48*x^66 + 13*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 95*x^25 + 116*x^23 + 32*x^22 + 69*x^21 + 30*x^19 + 80*x^18 + 7*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 105*x^9 + 68*x^7 + 32*x^6 + 59*x^5 + 106*x^3 + 112*x^2 + 41*x, x^93 + 74*x^91 + 32*x^90 + 35*x^89 + 32*x^88 + 68*x^87 + x^85 + 102*x^83 + 32*x^82 + 43*x^81 + 32*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 96*x^74 + 93*x^73 + 96*x^72 + 116*x^71 + 7*x^69 + 114*x^67 + 96*x^66 + 29*x^65 + 96*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 64*x^58 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 64*x^50 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 64*x^42 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 64*x^34 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 32*x^26 + 47*x^25 + 32*x^24 + 116*x^23 + 37*x^21 + 30*x^19 + 32*x^18 + 119*x^17 + 32*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 96*x^10 + 89*x^9 + 96*x^8 + 68*x^7 + 27*x^5 + 106*x^3 + 96*x^2 + 121*x + 96, x^93 + 74*x^91 + 100*x^90 + 75*x^89 + 52*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 76*x^82 + 67*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 85*x^73 + 60*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 68*x^66 + 101*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 119*x^25 + 68*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 60*x^18 + 111*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 113*x^9 + 76*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 52*x^2 + 33*x + 100, x^93 + 74*x^91 + 76*x^90 + 75*x^89 + 28*x^88 + 36*x^87 + 8*x^86 + 17*x^85 + 8*x^84 + 70*x^83 + 4*x^82 + 3*x^81 + 84*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 4*x^74 + 85*x^73 + 52*x^72 + 84*x^71 + 40*x^70 + 87*x^69 + 40*x^68 + 82*x^67 + 44*x^66 + 37*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 60*x^26 + 119*x^25 + 76*x^24 + 84*x^23 + 104*x^22 + 117*x^21 + 104*x^20 + 126*x^19 + 84*x^18 + 47*x^17 + 100*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 116*x^10 + 113*x^9 + 100*x^8 + 36*x^7 + 72*x^6 + 43*x^5 + 72*x^4 + 74*x^3 + 124*x^2 + 97*x + 108, x^93 + 74*x^91 + 12*x^90 + 11*x^89 + 28*x^88 + 100*x^87 + 72*x^86 + 81*x^85 + 72*x^84 + 6*x^83 + 4*x^82 + 3*x^81 + 20*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 68*x^74 + 21*x^73 + 52*x^72 + 20*x^71 + 104*x^70 + 23*x^69 + 104*x^68 + 18*x^67 + 44*x^66 + 37*x^65 + 28*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 78*x^57 + 88*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 104*x^50 + 30*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 42*x^41 + 40*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 24*x^34 + 42*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 55*x^25 + 76*x^24 + 20*x^23 + 40*x^22 + 53*x^21 + 40*x^20 + 62*x^19 + 84*x^18 + 47*x^17 + 36*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 52*x^10 + 49*x^9 + 100*x^8 + 100*x^7 + 8*x^6 + 107*x^5 + 8*x^4 + 10*x^3 + 124*x^2 + 97*x + 44, x^93 + 74*x^91 + 16*x^90 + 3*x^89 + 48*x^88 + 68*x^87 + 32*x^86 + 65*x^85 + 96*x^84 + 102*x^83 + 112*x^82 + 75*x^81 + 80*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 48*x^74 + 125*x^73 + 16*x^72 + 116*x^71 + 32*x^70 + 71*x^69 + 96*x^68 + 114*x^67 + 80*x^66 + 125*x^65 + 112*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 32*x^58 + 126*x^57 + 96*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 96*x^50 + 110*x^49 + 32*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 96*x^42 + 122*x^41 + 32*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 32*x^34 + 90*x^33 + 96*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 80*x^26 + 15*x^25 + 112*x^24 + 116*x^23 + 32*x^22 + 101*x^21 + 96*x^20 + 30*x^19 + 48*x^18 + 23*x^17 + 16*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 112*x^10 + 121*x^9 + 80*x^8 + 68*x^7 + 32*x^6 + 91*x^5 + 96*x^4 + 106*x^3 + 16*x^2 + 89*x + 48, x^93 + 74*x^91 + 100*x^90 + 123*x^89 + 100*x^88 + 36*x^87 + 88*x^86 + 49*x^85 + 56*x^84 + 70*x^83 + 76*x^82 + 19*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 101*x^73 + 76*x^72 + 84*x^71 + 56*x^70 + 119*x^69 + 24*x^68 + 82*x^67 + 68*x^66 + 85*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 46*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 62*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 74*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 10*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 103*x^25 + 52*x^24 + 84*x^23 + 120*x^22 + 21*x^21 + 88*x^20 + 126*x^19 + 60*x^18 + 127*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 65*x^9 + 28*x^8 + 36*x^7 + 24*x^6 + 75*x^5 + 120*x^4 + 74*x^3 + 52*x^2 + 81*x + 84, x^93 + 74*x^91 + 84*x^90 + 59*x^89 + 52*x^88 + 36*x^87 + 120*x^86 + 49*x^85 + 24*x^84 + 70*x^83 + 28*x^82 + 83*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 37*x^73 + 60*x^72 + 84*x^71 + 88*x^70 + 119*x^69 + 120*x^68 + 82*x^67 + 52*x^66 + 21*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 39*x^25 + 68*x^24 + 84*x^23 + 24*x^22 + 21*x^21 + 56*x^20 + 126*x^19 + 76*x^18 + 63*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + x^9 + 76*x^8 + 36*x^7 + 56*x^6 + 75*x^5 + 88*x^4 + 74*x^3 + 100*x^2 + 17*x + 100, x^93 + 74*x^91 + 100*x^90 + 43*x^89 + 52*x^88 + 100*x^87 + 88*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 76*x^82 + 99*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 117*x^73 + 60*x^72 + 20*x^71 + 56*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 68*x^66 + 69*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 87*x^25 + 68*x^24 + 20*x^23 + 120*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 60*x^18 + 15*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 17*x^9 + 76*x^8 + 100*x^7 + 24*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 52*x^2 + x + 100, x^93 + 74*x^91 + 44*x^90 + 59*x^89 + 108*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 36*x^82 + 19*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 37*x^73 + 36*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 12*x^66 + 85*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 39*x^25 + 92*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 116*x^18 + 127*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + x^9 + 20*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 92*x^2 + 81*x + 124, x^93 + 74*x^91 + 48*x^90 + 3*x^89 + 80*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 80*x^82 + 75*x^81 + 48*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 125*x^73 + 112*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 112*x^66 + 125*x^65 + 16*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 15*x^25 + 16*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 16*x^18 + 23*x^17 + 112*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 121*x^9 + 48*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 48*x^2 + 89*x + 80, x^93 + 74*x^91 + 104*x^90 + 51*x^89 + 56*x^88 + 4*x^87 + 112*x^86 + 33*x^85 + 16*x^84 + 38*x^83 + 120*x^82 + 27*x^81 + 40*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 13*x^73 + 104*x^72 + 52*x^71 + 48*x^70 + 39*x^69 + 80*x^68 + 50*x^67 + 40*x^66 + 109*x^65 + 56*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 127*x^25 + 24*x^24 + 52*x^23 + 48*x^22 + 69*x^21 + 80*x^20 + 94*x^19 + 88*x^18 + 39*x^17 + 72*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 73*x^9 + 72*x^8 + 4*x^7 + 112*x^6 + 59*x^5 + 16*x^4 + 42*x^3 + 8*x^2 + 9*x + 88, x^93 + 74*x^91 + 64*x^90 + 67*x^89 + 4*x^87 + x^85 + 38*x^83 + 64*x^82 + 75*x^81 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 61*x^73 + 52*x^71 + 7*x^69 + 50*x^67 + 64*x^66 + 125*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 79*x^25 + 52*x^23 + 37*x^21 + 94*x^19 + 64*x^18 + 23*x^17 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 57*x^9 + 4*x^7 + 27*x^5 + 42*x^3 + 64*x^2 + 89*x, x^93 + 74*x^91 + 108*x^90 + 91*x^89 + 108*x^88 + 100*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 6*x^83 + 100*x^82 + 115*x^81 + 68*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 100*x^74 + 5*x^73 + 36*x^72 + 20*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 18*x^67 + 76*x^66 + 117*x^65 + 44*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 110*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 126*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 10*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 74*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 71*x^25 + 92*x^24 + 20*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 62*x^19 + 52*x^18 + 95*x^17 + 20*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 84*x^10 + 97*x^9 + 20*x^8 + 100*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 10*x^3 + 28*x^2 + 113*x + 124, x^93 + 74*x^91 + 48*x^90 + 83*x^89 + 64*x^88 + 4*x^87 + 96*x^86 + 97*x^85 + 64*x^84 + 38*x^83 + 80*x^82 + 123*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 16*x^74 + 109*x^73 + 64*x^72 + 52*x^71 + 96*x^70 + 103*x^69 + 64*x^68 + 50*x^67 + 112*x^66 + 13*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 31*x^25 + 64*x^24 + 52*x^23 + 96*x^22 + 5*x^21 + 64*x^20 + 94*x^19 + 16*x^18 + 7*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 80*x^10 + 41*x^9 + 64*x^8 + 4*x^7 + 96*x^6 + 123*x^5 + 64*x^4 + 42*x^3 + 48*x^2 + 41*x, x^93 + 74*x^91 + 24*x^90 + 51*x^89 + 8*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 8*x^82 + 27*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 13*x^73 + 88*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 88*x^66 + 109*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 127*x^25 + 40*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 40*x^18 + 39*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 73*x^9 + 120*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 120*x^2 + 9*x + 104, x^93 + 74*x^91 + 108*x^90 + 75*x^89 + 60*x^88 + 36*x^87 + 72*x^86 + 17*x^85 + 72*x^84 + 70*x^83 + 100*x^82 + 3*x^81 + 52*x^80 + 88*x^79 + 112*x^78 + 15*x^77 + 112*x^76 + 126*x^75 + 100*x^74 + 85*x^73 + 20*x^72 + 84*x^71 + 104*x^70 + 87*x^69 + 104*x^68 + 82*x^67 + 76*x^66 + 37*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 78*x^57 + 24*x^56 + 8*x^55 + 16*x^54 + 106*x^53 + 16*x^52 + 28*x^51 + 40*x^50 + 30*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 42*x^41 + 104*x^40 + 8*x^39 + 16*x^38 + 14*x^37 + 16*x^36 + 4*x^35 + 88*x^34 + 42*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 92*x^26 + 119*x^25 + 108*x^24 + 84*x^23 + 40*x^22 + 117*x^21 + 40*x^20 + 126*x^19 + 52*x^18 + 47*x^17 + 68*x^16 + 88*x^15 + 112*x^14 + 99*x^13 + 112*x^12 + 70*x^11 + 84*x^10 + 113*x^9 + 68*x^8 + 36*x^7 + 8*x^6 + 43*x^5 + 8*x^4 + 74*x^3 + 28*x^2 + 97*x + 12, x^93 + 74*x^91 + 40*x^90 + 19*x^89 + 24*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 56*x^82 + 59*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 56*x^74 + 45*x^73 + 8*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 104*x^66 + 77*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 72*x^26 + 95*x^25 + 120*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 24*x^18 + 71*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 88*x^10 + 105*x^9 + 104*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 72*x^2 + 105*x + 56, x^93 + 74*x^91 + 84*x^90 + 91*x^89 + 116*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 92*x^82 + 115*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 5*x^73 + 124*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 116*x^66 + 117*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 71*x^25 + 4*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 12*x^18 + 95*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 97*x^9 + 12*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 36*x^2 + 113*x + 100, x^93 + 74*x^91 + 68*x^90 + 43*x^89 + 52*x^88 + 36*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 70*x^83 + 44*x^82 + 35*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 117*x^73 + 60*x^72 + 84*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 82*x^67 + 100*x^66 + 5*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 87*x^25 + 68*x^24 + 84*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 126*x^19 + 28*x^18 + 79*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 17*x^9 + 76*x^8 + 36*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 74*x^3 + 84*x^2 + 65*x + 36, x^93 + 74*x^91 + 100*x^90 + 91*x^89 + 4*x^88 + 100*x^87 + 24*x^86 + 49*x^85 + 56*x^84 + 6*x^83 + 12*x^82 + 115*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 12*x^74 + 5*x^73 + 44*x^72 + 20*x^71 + 120*x^70 + 119*x^69 + 24*x^68 + 18*x^67 + 4*x^66 + 117*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 56*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 72*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 71*x^25 + 84*x^24 + 20*x^23 + 56*x^22 + 21*x^21 + 88*x^20 + 62*x^19 + 124*x^18 + 95*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 92*x^10 + 97*x^9 + 124*x^8 + 100*x^7 + 88*x^6 + 75*x^5 + 120*x^4 + 10*x^3 + 116*x^2 + 113*x + 52, x^93 + 74*x^91 + 8*x^90 + 51*x^89 + 56*x^88 + 68*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 102*x^83 + 24*x^82 + 91*x^81 + 104*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 88*x^74 + 13*x^73 + 104*x^72 + 116*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 114*x^67 + 8*x^66 + 45*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 94*x^57 + 48*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 112*x^50 + 14*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 26*x^41 + 80*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 16*x^34 + 58*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 40*x^26 + 127*x^25 + 24*x^24 + 116*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 30*x^19 + 120*x^18 + 103*x^17 + 8*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 120*x^10 + 73*x^9 + 72*x^8 + 68*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 106*x^3 + 104*x^2 + 73*x + 24, x^93 + 74*x^91 + 64*x^90 + 35*x^89 + 96*x^88 + 68*x^87 + 64*x^86 + x^85 + 102*x^83 + 43*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 93*x^73 + 32*x^72 + 116*x^71 + 64*x^70 + 7*x^69 + 114*x^67 + 29*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 62*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 46*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 58*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 26*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 47*x^25 + 96*x^24 + 116*x^23 + 64*x^22 + 37*x^21 + 30*x^19 + 119*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 89*x^9 + 32*x^8 + 68*x^7 + 64*x^6 + 27*x^5 + 106*x^3 + 121*x + 32, x^93 + 74*x^91 + 124*x^90 + 59*x^89 + 60*x^88 + 100*x^87 + 40*x^86 + 113*x^85 + 72*x^84 + 6*x^83 + 20*x^82 + 19*x^81 + 52*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 20*x^74 + 37*x^73 + 20*x^72 + 20*x^71 + 72*x^70 + 55*x^69 + 104*x^68 + 18*x^67 + 92*x^66 + 85*x^65 + 124*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 46*x^57 + 24*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 8*x^50 + 62*x^49 + 72*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 74*x^41 + 104*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 120*x^34 + 10*x^33 + 56*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 44*x^26 + 39*x^25 + 108*x^24 + 20*x^23 + 8*x^22 + 85*x^21 + 40*x^20 + 62*x^19 + 36*x^18 + 127*x^17 + 68*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 68*x^10 + x^9 + 68*x^8 + 100*x^7 + 104*x^6 + 11*x^5 + 8*x^4 + 10*x^3 + 108*x^2 + 81*x + 12, x^93 + 74*x^91 + 100*x^90 + 11*x^89 + 116*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 24*x^84 + 6*x^83 + 76*x^82 + 3*x^81 + 28*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 21*x^73 + 124*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 120*x^68 + 18*x^67 + 68*x^66 + 37*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 55*x^25 + 4*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 56*x^20 + 62*x^19 + 60*x^18 + 47*x^17 + 76*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 49*x^9 + 12*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 88*x^4 + 10*x^3 + 52*x^2 + 97*x + 36, x^93 + 74*x^91 + 120*x^90 + 51*x^89 + 72*x^88 + 4*x^87 + 80*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 40*x^82 + 27*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 13*x^73 + 24*x^72 + 52*x^71 + 16*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 56*x^66 + 109*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 127*x^25 + 104*x^24 + 52*x^23 + 16*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 72*x^18 + 39*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 73*x^9 + 56*x^8 + 4*x^7 + 80*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 88*x^2 + 9*x + 40, x^93 + 74*x^91 + 68*x^90 + 27*x^89 + 68*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 108*x^82 + 115*x^81 + 12*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 69*x^73 + 108*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 36*x^66 + 117*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 7*x^25 + 20*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 92*x^18 + 95*x^17 + 124*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 33*x^9 + 60*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 20*x^2 + 113*x + 52, x^93 + 74*x^91 + 28*x^90 + 123*x^89 + 28*x^88 + 100*x^87 + 104*x^86 + 113*x^85 + 8*x^84 + 6*x^83 + 116*x^82 + 83*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 116*x^74 + 101*x^73 + 52*x^72 + 20*x^71 + 8*x^70 + 55*x^69 + 40*x^68 + 18*x^67 + 124*x^66 + 21*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 76*x^26 + 103*x^25 + 76*x^24 + 20*x^23 + 72*x^22 + 85*x^21 + 104*x^20 + 62*x^19 + 4*x^18 + 63*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 36*x^10 + 65*x^9 + 100*x^8 + 100*x^7 + 40*x^6 + 11*x^5 + 72*x^4 + 10*x^3 + 12*x^2 + 17*x + 108, x^93 + 74*x^91 + 12*x^90 + 123*x^89 + 76*x^88 + 36*x^87 + 72*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 4*x^82 + 19*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 68*x^74 + 101*x^73 + 68*x^72 + 84*x^71 + 104*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 44*x^66 + 85*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 56*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 104*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 72*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 24*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 124*x^26 + 103*x^25 + 60*x^24 + 84*x^23 + 40*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 84*x^18 + 127*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 52*x^10 + 65*x^9 + 52*x^8 + 36*x^7 + 8*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 124*x^2 + 81*x + 28, x^93 + 74*x^91 + 44*x^90 + 59*x^89 + 44*x^88 + 100*x^87 + 72*x^86 + 113*x^85 + 104*x^84 + 6*x^83 + 36*x^82 + 19*x^81 + 4*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 37*x^73 + 100*x^72 + 20*x^71 + 104*x^70 + 55*x^69 + 8*x^68 + 18*x^67 + 12*x^66 + 85*x^65 + 108*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 120*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 104*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 8*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 24*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 39*x^25 + 28*x^24 + 20*x^23 + 40*x^22 + 85*x^21 + 72*x^20 + 62*x^19 + 116*x^18 + 127*x^17 + 84*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + x^9 + 84*x^8 + 100*x^7 + 8*x^6 + 11*x^5 + 40*x^4 + 10*x^3 + 92*x^2 + 81*x + 60, x^93 + 74*x^91 + 104*x^90 + 83*x^89 + 24*x^88 + 4*x^87 + 112*x^86 + 97*x^85 + 80*x^84 + 38*x^83 + 120*x^82 + 123*x^81 + 72*x^80 + 24*x^79 + 32*x^78 + 111*x^77 + 96*x^76 + 62*x^75 + 120*x^74 + 109*x^73 + 8*x^72 + 52*x^71 + 48*x^70 + 103*x^69 + 16*x^68 + 50*x^67 + 40*x^66 + 13*x^65 + 24*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 16*x^58 + 30*x^57 + 112*x^56 + 72*x^55 + 96*x^54 + 10*x^53 + 32*x^52 + 92*x^51 + 48*x^50 + 78*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 112*x^42 + 90*x^41 + 16*x^40 + 72*x^39 + 96*x^38 + 46*x^37 + 32*x^36 + 68*x^35 + 80*x^34 + 122*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 8*x^26 + 31*x^25 + 120*x^24 + 52*x^23 + 48*x^22 + 5*x^21 + 16*x^20 + 94*x^19 + 88*x^18 + 7*x^17 + 104*x^16 + 24*x^15 + 32*x^14 + 67*x^13 + 96*x^12 + 6*x^11 + 24*x^10 + 41*x^9 + 104*x^8 + 4*x^7 + 112*x^6 + 123*x^5 + 80*x^4 + 42*x^3 + 8*x^2 + 41*x + 56, x^93 + 74*x^91 + 120*x^90 + 51*x^89 + 72*x^88 + 68*x^87 + 16*x^86 + 97*x^85 + 48*x^84 + 102*x^83 + 104*x^82 + 91*x^81 + 24*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 40*x^74 + 13*x^73 + 24*x^72 + 116*x^71 + 80*x^70 + 103*x^69 + 112*x^68 + 114*x^67 + 120*x^66 + 45*x^65 + 8*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 16*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 112*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 127*x^25 + 104*x^24 + 116*x^23 + 80*x^22 + 5*x^21 + 112*x^20 + 30*x^19 + 8*x^18 + 103*x^17 + 120*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 8*x^10 + 73*x^9 + 56*x^8 + 68*x^7 + 16*x^6 + 123*x^5 + 48*x^4 + 106*x^3 + 24*x^2 + 73*x + 104, x^93 + 74*x^91 + 20*x^90 + 75*x^89 + 4*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 28*x^82 + 3*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 28*x^74 + 85*x^73 + 44*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 52*x^66 + 37*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 119*x^25 + 84*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 76*x^18 + 47*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 44*x^10 + 113*x^9 + 124*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 100*x^2 + 97*x + 52, x^93 + 74*x^91 + 68*x^90 + 43*x^89 + 52*x^88 + 100*x^87 + 24*x^86 + 17*x^85 + 24*x^84 + 6*x^83 + 108*x^82 + 99*x^81 + 92*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 44*x^74 + 117*x^73 + 60*x^72 + 20*x^71 + 120*x^70 + 87*x^69 + 120*x^68 + 18*x^67 + 36*x^66 + 69*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 14*x^57 + 72*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 120*x^50 + 94*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 106*x^41 + 56*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 8*x^34 + 106*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 87*x^25 + 68*x^24 + 20*x^23 + 56*x^22 + 117*x^21 + 56*x^20 + 62*x^19 + 92*x^18 + 15*x^17 + 12*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 124*x^10 + 17*x^9 + 76*x^8 + 100*x^7 + 88*x^6 + 43*x^5 + 88*x^4 + 10*x^3 + 20*x^2 + x + 100, x^93 + 74*x^91 + 100*x^90 + 75*x^89 + 84*x^88 + 100*x^87 + 88*x^86 + 81*x^85 + 88*x^84 + 6*x^83 + 76*x^82 + 67*x^81 + 60*x^80 + 88*x^79 + 80*x^78 + 15*x^77 + 80*x^76 + 126*x^75 + 12*x^74 + 85*x^73 + 28*x^72 + 20*x^71 + 56*x^70 + 23*x^69 + 56*x^68 + 18*x^67 + 68*x^66 + 101*x^65 + 84*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 40*x^58 + 78*x^57 + 8*x^56 + 8*x^55 + 48*x^54 + 106*x^53 + 48*x^52 + 28*x^51 + 56*x^50 + 30*x^49 + 24*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 88*x^42 + 42*x^41 + 120*x^40 + 8*x^39 + 48*x^38 + 14*x^37 + 48*x^36 + 4*x^35 + 72*x^34 + 42*x^33 + 104*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 52*x^26 + 119*x^25 + 100*x^24 + 20*x^23 + 120*x^22 + 53*x^21 + 120*x^20 + 62*x^19 + 60*x^18 + 111*x^17 + 108*x^16 + 88*x^15 + 80*x^14 + 99*x^13 + 80*x^12 + 70*x^11 + 92*x^10 + 113*x^9 + 44*x^8 + 100*x^7 + 24*x^6 + 107*x^5 + 24*x^4 + 10*x^3 + 52*x^2 + 33*x + 4, x^93 + 74*x^91 + 64*x^90 + 67*x^89 + 96*x^88 + 68*x^87 + 64*x^86 + 65*x^85 + 102*x^83 + 11*x^81 + 96*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 64*x^74 + 61*x^73 + 32*x^72 + 116*x^71 + 64*x^70 + 71*x^69 + 114*x^67 + 61*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 64*x^56 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 64*x^40 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 64*x^26 + 79*x^25 + 96*x^24 + 116*x^23 + 64*x^22 + 101*x^21 + 30*x^19 + 87*x^17 + 96*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 64*x^10 + 57*x^9 + 32*x^8 + 68*x^7 + 64*x^6 + 91*x^5 + 106*x^3 + 25*x + 32, x^93 + 74*x^91 + 20*x^90 + 59*x^89 + 116*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 28*x^82 + 19*x^81 + 92*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 28*x^74 + 37*x^73 + 124*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 52*x^66 + 85*x^65 + 52*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 36*x^26 + 39*x^25 + 4*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 76*x^18 + 127*x^17 + 12*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 44*x^10 + x^9 + 12*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 100*x^2 + 81*x + 100, x^93 + 74*x^91 + 116*x^90 + 43*x^89 + 68*x^88 + 36*x^87 + 120*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 60*x^82 + 35*x^81 + 76*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 60*x^74 + 117*x^73 + 108*x^72 + 84*x^71 + 88*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 20*x^66 + 5*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 72*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 24*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 56*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 104*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 4*x^26 + 87*x^25 + 20*x^24 + 84*x^23 + 24*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 108*x^18 + 79*x^17 + 60*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 76*x^10 + 17*x^9 + 60*x^8 + 36*x^7 + 56*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 68*x^2 + 65*x + 116, x^93 + 74*x^91 + 92*x^90 + 123*x^89 + 92*x^88 + 36*x^87 + 40*x^86 + 49*x^85 + 72*x^84 + 70*x^83 + 116*x^82 + 19*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 101*x^73 + 116*x^72 + 84*x^71 + 72*x^70 + 119*x^69 + 104*x^68 + 82*x^67 + 124*x^66 + 85*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 46*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 62*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 74*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 10*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 103*x^25 + 12*x^24 + 84*x^23 + 8*x^22 + 21*x^21 + 40*x^20 + 126*x^19 + 4*x^18 + 127*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 65*x^9 + 36*x^8 + 36*x^7 + 104*x^6 + 75*x^5 + 8*x^4 + 74*x^3 + 12*x^2 + 81*x + 108, x^93 + 74*x^91 + 120*x^90 + 67*x^89 + 24*x^88 + 4*x^87 + 16*x^86 + x^85 + 16*x^84 + 38*x^83 + 104*x^82 + 75*x^81 + 8*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 40*x^74 + 61*x^73 + 8*x^72 + 52*x^71 + 80*x^70 + 7*x^69 + 80*x^68 + 50*x^67 + 120*x^66 + 125*x^65 + 88*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 48*x^58 + 126*x^57 + 112*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 16*x^50 + 110*x^49 + 80*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 80*x^42 + 122*x^41 + 16*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 112*x^34 + 90*x^33 + 48*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 88*x^26 + 79*x^25 + 120*x^24 + 52*x^23 + 80*x^22 + 37*x^21 + 80*x^20 + 94*x^19 + 8*x^18 + 23*x^17 + 40*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 8*x^10 + 57*x^9 + 104*x^8 + 4*x^7 + 16*x^6 + 27*x^5 + 16*x^4 + 42*x^3 + 24*x^2 + 89*x + 120, x^93 + 74*x^91 + 4*x^90 + 27*x^89 + 4*x^88 + 36*x^87 + 24*x^86 + 113*x^85 + 120*x^84 + 70*x^83 + 44*x^82 + 115*x^81 + 76*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 108*x^74 + 69*x^73 + 44*x^72 + 84*x^71 + 120*x^70 + 55*x^69 + 88*x^68 + 82*x^67 + 100*x^66 + 117*x^65 + 4*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 104*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 24*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 84*x^26 + 7*x^25 + 84*x^24 + 84*x^23 + 56*x^22 + 85*x^21 + 24*x^20 + 126*x^19 + 28*x^18 + 95*x^17 + 60*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 60*x^10 + 33*x^9 + 124*x^8 + 36*x^7 + 88*x^6 + 11*x^5 + 56*x^4 + 74*x^3 + 84*x^2 + 113*x + 116, x^93 + 74*x^91 + 24*x^90 + 3*x^89 + 120*x^88 + 68*x^87 + 16*x^86 + 65*x^85 + 16*x^84 + 102*x^83 + 8*x^82 + 75*x^81 + 104*x^80 + 24*x^79 + 96*x^78 + 47*x^77 + 96*x^76 + 62*x^75 + 8*x^74 + 125*x^73 + 40*x^72 + 116*x^71 + 80*x^70 + 71*x^69 + 80*x^68 + 114*x^67 + 88*x^66 + 125*x^65 + 120*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 126*x^57 + 48*x^56 + 72*x^55 + 32*x^54 + 74*x^53 + 32*x^52 + 92*x^51 + 80*x^50 + 110*x^49 + 16*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 122*x^41 + 80*x^40 + 72*x^39 + 32*x^38 + 110*x^37 + 32*x^36 + 68*x^35 + 48*x^34 + 90*x^33 + 112*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 15*x^25 + 88*x^24 + 116*x^23 + 80*x^22 + 101*x^21 + 80*x^20 + 30*x^19 + 40*x^18 + 23*x^17 + 8*x^16 + 24*x^15 + 96*x^14 + 3*x^13 + 96*x^12 + 6*x^11 + 104*x^10 + 121*x^9 + 8*x^8 + 68*x^7 + 16*x^6 + 91*x^5 + 16*x^4 + 106*x^3 + 120*x^2 + 89*x + 24, x^93 + 74*x^91 + 84*x^90 + 27*x^89 + 52*x^88 + 100*x^87 + 56*x^86 + 49*x^85 + 88*x^84 + 6*x^83 + 92*x^82 + 51*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 69*x^73 + 60*x^72 + 20*x^71 + 24*x^70 + 119*x^69 + 56*x^68 + 18*x^67 + 116*x^66 + 53*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 110*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 126*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 10*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 74*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 7*x^25 + 68*x^24 + 20*x^23 + 88*x^22 + 21*x^21 + 120*x^20 + 62*x^19 + 12*x^18 + 31*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 33*x^9 + 76*x^8 + 100*x^7 + 120*x^6 + 75*x^5 + 24*x^4 + 10*x^3 + 36*x^2 + 49*x + 36, x^93 + 74*x^91 + 68*x^90 + 27*x^89 + 36*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 44*x^82 + 51*x^81 + 108*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 69*x^73 + 12*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 100*x^66 + 53*x^65 + 100*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 7*x^25 + 116*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 28*x^18 + 31*x^17 + 92*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 33*x^9 + 92*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 84*x^2 + 49*x + 84, x^93 + 74*x^91 + 72*x^90 + 3*x^89 + 8*x^88 + 4*x^87 + 112*x^86 + x^85 + 48*x^84 + 38*x^83 + 88*x^82 + 11*x^81 + 88*x^80 + 24*x^79 + 32*x^78 + 47*x^77 + 32*x^76 + 62*x^75 + 24*x^74 + 125*x^73 + 88*x^72 + 52*x^71 + 48*x^70 + 7*x^69 + 112*x^68 + 50*x^67 + 72*x^66 + 61*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 80*x^58 + 126*x^57 + 80*x^56 + 72*x^55 + 96*x^54 + 74*x^53 + 96*x^52 + 92*x^51 + 112*x^50 + 110*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 48*x^42 + 122*x^41 + 48*x^40 + 72*x^39 + 96*x^38 + 110*x^37 + 96*x^36 + 68*x^35 + 16*x^34 + 90*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 104*x^26 + 15*x^25 + 40*x^24 + 52*x^23 + 48*x^22 + 37*x^21 + 112*x^20 + 94*x^19 + 56*x^18 + 87*x^17 + 56*x^16 + 24*x^15 + 32*x^14 + 3*x^13 + 32*x^12 + 6*x^11 + 56*x^10 + 121*x^9 + 120*x^8 + 4*x^7 + 112*x^6 + 27*x^5 + 48*x^4 + 42*x^3 + 40*x^2 + 25*x + 40, x^93 + 74*x^91 + 44*x^90 + 123*x^89 + 76*x^88 + 36*x^87 + 8*x^86 + 49*x^85 + 104*x^84 + 70*x^83 + 100*x^82 + 19*x^81 + 36*x^80 + 88*x^79 + 112*x^78 + 79*x^77 + 48*x^76 + 126*x^75 + 36*x^74 + 101*x^73 + 68*x^72 + 84*x^71 + 40*x^70 + 119*x^69 + 8*x^68 + 82*x^67 + 76*x^66 + 85*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 120*x^58 + 46*x^57 + 56*x^56 + 8*x^55 + 16*x^54 + 42*x^53 + 80*x^52 + 28*x^51 + 40*x^50 + 62*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 8*x^42 + 74*x^41 + 72*x^40 + 8*x^39 + 16*x^38 + 78*x^37 + 80*x^36 + 4*x^35 + 88*x^34 + 10*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 28*x^26 + 103*x^25 + 60*x^24 + 84*x^23 + 104*x^22 + 21*x^21 + 72*x^20 + 126*x^19 + 52*x^18 + 127*x^17 + 116*x^16 + 88*x^15 + 112*x^14 + 35*x^13 + 48*x^12 + 70*x^11 + 20*x^10 + 65*x^9 + 52*x^8 + 36*x^7 + 72*x^6 + 75*x^5 + 40*x^4 + 74*x^3 + 28*x^2 + 81*x + 28, x^93 + 74*x^91 + 112*x^90 + 19*x^89 + 68*x^87 + 32*x^86 + 33*x^85 + 102*x^83 + 80*x^82 + 123*x^81 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 45*x^73 + 116*x^71 + 32*x^70 + 39*x^69 + 114*x^67 + 112*x^66 + 13*x^65 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 30*x^57 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 78*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 90*x^41 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 122*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 95*x^25 + 116*x^23 + 32*x^22 + 69*x^21 + 30*x^19 + 16*x^18 + 7*x^17 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 105*x^9 + 68*x^7 + 32*x^6 + 59*x^5 + 106*x^3 + 48*x^2 + 41*x, x^93 + 74*x^91 + 48*x^90 + 3*x^89 + 16*x^88 + 68*x^87 + 96*x^86 + 65*x^85 + 32*x^84 + 102*x^83 + 80*x^82 + 75*x^81 + 112*x^80 + 24*x^79 + 64*x^78 + 47*x^77 + 64*x^76 + 62*x^75 + 16*x^74 + 125*x^73 + 48*x^72 + 116*x^71 + 96*x^70 + 71*x^69 + 32*x^68 + 114*x^67 + 112*x^66 + 125*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 126*x^57 + 32*x^56 + 72*x^55 + 64*x^54 + 74*x^53 + 64*x^52 + 92*x^51 + 32*x^50 + 110*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 122*x^41 + 96*x^40 + 72*x^39 + 64*x^38 + 110*x^37 + 64*x^36 + 68*x^35 + 96*x^34 + 90*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 112*x^26 + 15*x^25 + 80*x^24 + 116*x^23 + 96*x^22 + 101*x^21 + 32*x^20 + 30*x^19 + 16*x^18 + 23*x^17 + 48*x^16 + 24*x^15 + 64*x^14 + 3*x^13 + 64*x^12 + 6*x^11 + 80*x^10 + 121*x^9 + 112*x^8 + 68*x^7 + 96*x^6 + 91*x^5 + 32*x^4 + 106*x^3 + 48*x^2 + 89*x + 16, x^93 + 74*x^91 + 84*x^90 + 11*x^89 + 4*x^88 + 36*x^87 + 56*x^86 + 17*x^85 + 56*x^84 + 70*x^83 + 92*x^82 + 67*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 21*x^73 + 44*x^72 + 84*x^71 + 24*x^70 + 87*x^69 + 24*x^68 + 82*x^67 + 116*x^66 + 101*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 78*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 30*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 42*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 42*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 55*x^25 + 84*x^24 + 84*x^23 + 88*x^22 + 117*x^21 + 88*x^20 + 126*x^19 + 12*x^18 + 111*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 49*x^9 + 124*x^8 + 36*x^7 + 120*x^6 + 43*x^5 + 120*x^4 + 74*x^3 + 36*x^2 + 33*x + 52, x^93 + 74*x^91 + 24*x^90 + 115*x^89 + 72*x^88 + 4*x^87 + 16*x^86 + 33*x^85 + 112*x^84 + 38*x^83 + 8*x^82 + 91*x^81 + 88*x^80 + 24*x^79 + 96*x^78 + 111*x^77 + 32*x^76 + 62*x^75 + 8*x^74 + 77*x^73 + 24*x^72 + 52*x^71 + 80*x^70 + 39*x^69 + 48*x^68 + 50*x^67 + 88*x^66 + 45*x^65 + 72*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 112*x^58 + 94*x^57 + 80*x^56 + 72*x^55 + 32*x^54 + 10*x^53 + 96*x^52 + 92*x^51 + 80*x^50 + 14*x^49 + 112*x^48 + 16*x^47 + 64*x^46 + 30*x^45 + 64*x^44 + 28*x^43 + 16*x^42 + 26*x^41 + 48*x^40 + 72*x^39 + 32*x^38 + 46*x^37 + 96*x^36 + 68*x^35 + 48*x^34 + 58*x^33 + 16*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 120*x^26 + 63*x^25 + 104*x^24 + 52*x^23 + 80*x^22 + 69*x^21 + 48*x^20 + 94*x^19 + 40*x^18 + 103*x^17 + 56*x^16 + 24*x^15 + 96*x^14 + 67*x^13 + 32*x^12 + 6*x^11 + 104*x^10 + 9*x^9 + 56*x^8 + 4*x^7 + 16*x^6 + 59*x^5 + 112*x^4 + 42*x^3 + 120*x^2 + 73*x + 40, x^93 + 74*x^91 + 60*x^90 + 11*x^89 + 12*x^88 + 36*x^87 + 40*x^86 + 17*x^85 + 40*x^84 + 70*x^83 + 84*x^82 + 67*x^81 + 36*x^80 + 88*x^79 + 48*x^78 + 15*x^77 + 48*x^76 + 126*x^75 + 84*x^74 + 21*x^73 + 4*x^72 + 84*x^71 + 72*x^70 + 87*x^69 + 72*x^68 + 82*x^67 + 28*x^66 + 101*x^65 + 76*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 24*x^58 + 78*x^57 + 56*x^56 + 8*x^55 + 80*x^54 + 106*x^53 + 80*x^52 + 28*x^51 + 8*x^50 + 30*x^49 + 40*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 104*x^42 + 42*x^41 + 72*x^40 + 8*x^39 + 80*x^38 + 14*x^37 + 80*x^36 + 4*x^35 + 120*x^34 + 42*x^33 + 88*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 108*x^26 + 55*x^25 + 124*x^24 + 84*x^23 + 8*x^22 + 117*x^21 + 8*x^20 + 126*x^19 + 100*x^18 + 111*x^17 + 116*x^16 + 88*x^15 + 48*x^14 + 99*x^13 + 48*x^12 + 70*x^11 + 4*x^10 + 49*x^9 + 116*x^8 + 36*x^7 + 104*x^6 + 43*x^5 + 104*x^4 + 74*x^3 + 44*x^2 + 33*x + 28, x^93 + 74*x^91 + 92*x^90 + 27*x^89 + 28*x^88 + 100*x^87 + 104*x^86 + 49*x^85 + 8*x^84 + 6*x^83 + 52*x^82 + 51*x^81 + 84*x^80 + 88*x^79 + 48*x^78 + 79*x^77 + 112*x^76 + 126*x^75 + 52*x^74 + 69*x^73 + 52*x^72 + 20*x^71 + 8*x^70 + 119*x^69 + 40*x^68 + 18*x^67 + 60*x^66 + 53*x^65 + 92*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 88*x^58 + 110*x^57 + 88*x^56 + 8*x^55 + 80*x^54 + 42*x^53 + 16*x^52 + 28*x^51 + 72*x^50 + 126*x^49 + 8*x^48 + 16*x^47 + 32*x^46 + 94*x^45 + 32*x^44 + 28*x^43 + 40*x^42 + 10*x^41 + 40*x^40 + 8*x^39 + 80*x^38 + 78*x^37 + 16*x^36 + 4*x^35 + 56*x^34 + 74*x^33 + 120*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 12*x^26 + 7*x^25 + 76*x^24 + 20*x^23 + 72*x^22 + 21*x^21 + 104*x^20 + 62*x^19 + 68*x^18 + 31*x^17 + 100*x^16 + 88*x^15 + 48*x^14 + 35*x^13 + 112*x^12 + 70*x^11 + 100*x^10 + 33*x^9 + 100*x^8 + 100*x^7 + 40*x^6 + 75*x^5 + 72*x^4 + 10*x^3 + 76*x^2 + 49*x + 108, x^93 + 74*x^91 + 68*x^90 + 91*x^89 + 100*x^88 + 100*x^87 + 88*x^86 + 49*x^85 + 120*x^84 + 6*x^83 + 44*x^82 + 115*x^81 + 44*x^80 + 88*x^79 + 80*x^78 + 79*x^77 + 16*x^76 + 126*x^75 + 44*x^74 + 5*x^73 + 76*x^72 + 20*x^71 + 56*x^70 + 119*x^69 + 88*x^68 + 18*x^67 + 100*x^66 + 117*x^65 + 36*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 104*x^58 + 110*x^57 + 40*x^56 + 8*x^55 + 48*x^54 + 42*x^53 + 112*x^52 + 28*x^51 + 120*x^50 + 126*x^49 + 120*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 24*x^42 + 10*x^41 + 88*x^40 + 8*x^39 + 48*x^38 + 78*x^37 + 112*x^36 + 4*x^35 + 8*x^34 + 74*x^33 + 8*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 20*x^26 + 71*x^25 + 52*x^24 + 20*x^23 + 120*x^22 + 21*x^21 + 24*x^20 + 62*x^19 + 28*x^18 + 95*x^17 + 28*x^16 + 88*x^15 + 80*x^14 + 35*x^13 + 16*x^12 + 70*x^11 + 124*x^10 + 97*x^9 + 28*x^8 + 100*x^7 + 24*x^6 + 75*x^5 + 56*x^4 + 10*x^3 + 84*x^2 + 113*x + 20, x^93 + 74*x^91 + 3*x^89 + 68*x^87 + 64*x^86 + 65*x^85 + 64*x^84 + 102*x^83 + 64*x^82 + 75*x^81 + 64*x^80 + 24*x^79 + 47*x^77 + 62*x^75 + 125*x^73 + 116*x^71 + 64*x^70 + 71*x^69 + 64*x^68 + 114*x^67 + 64*x^66 + 125*x^65 + 64*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 126*x^57 + 72*x^55 + 74*x^53 + 92*x^51 + 110*x^49 + 16*x^47 + 30*x^45 + 28*x^43 + 122*x^41 + 72*x^39 + 110*x^37 + 68*x^35 + 90*x^33 + 32*x^31 + 69*x^29 + 82*x^27 + 15*x^25 + 116*x^23 + 64*x^22 + 101*x^21 + 64*x^20 + 30*x^19 + 64*x^18 + 23*x^17 + 64*x^16 + 24*x^15 + 3*x^13 + 6*x^11 + 121*x^9 + 68*x^7 + 64*x^6 + 91*x^5 + 64*x^4 + 106*x^3 + 64*x^2 + 89*x + 64, x^93 + 74*x^91 + 84*x^90 + 123*x^89 + 52*x^88 + 100*x^87 + 56*x^86 + 113*x^85 + 88*x^84 + 6*x^83 + 92*x^82 + 83*x^81 + 28*x^80 + 88*x^79 + 16*x^78 + 79*x^77 + 80*x^76 + 126*x^75 + 92*x^74 + 101*x^73 + 60*x^72 + 20*x^71 + 24*x^70 + 55*x^69 + 56*x^68 + 18*x^67 + 116*x^66 + 21*x^65 + 116*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 46*x^57 + 72*x^56 + 8*x^55 + 112*x^54 + 42*x^53 + 48*x^52 + 28*x^51 + 88*x^50 + 62*x^49 + 88*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 74*x^41 + 56*x^40 + 8*x^39 + 112*x^38 + 78*x^37 + 48*x^36 + 4*x^35 + 40*x^34 + 10*x^33 + 40*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 103*x^25 + 68*x^24 + 20*x^23 + 88*x^22 + 85*x^21 + 120*x^20 + 62*x^19 + 12*x^18 + 63*x^17 + 76*x^16 + 88*x^15 + 16*x^14 + 35*x^13 + 80*x^12 + 70*x^11 + 108*x^10 + 65*x^9 + 76*x^8 + 100*x^7 + 120*x^6 + 11*x^5 + 24*x^4 + 10*x^3 + 36*x^2 + 17*x + 36, x^93 + 74*x^91 + 112*x^90 + 51*x^89 + 96*x^88 + 4*x^87 + 96*x^86 + 33*x^85 + 38*x^83 + 16*x^82 + 27*x^81 + 96*x^80 + 24*x^79 + 64*x^78 + 111*x^77 + 62*x^75 + 80*x^74 + 13*x^73 + 32*x^72 + 52*x^71 + 96*x^70 + 39*x^69 + 50*x^67 + 48*x^66 + 109*x^65 + 32*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 96*x^58 + 94*x^57 + 64*x^56 + 72*x^55 + 64*x^54 + 10*x^53 + 92*x^51 + 32*x^50 + 14*x^49 + 64*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 32*x^42 + 26*x^41 + 64*x^40 + 72*x^39 + 64*x^38 + 46*x^37 + 68*x^35 + 96*x^34 + 58*x^33 + 64*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 48*x^26 + 127*x^25 + 96*x^24 + 52*x^23 + 96*x^22 + 69*x^21 + 94*x^19 + 80*x^18 + 39*x^17 + 96*x^16 + 24*x^15 + 64*x^14 + 67*x^13 + 6*x^11 + 16*x^10 + 73*x^9 + 32*x^8 + 4*x^7 + 96*x^6 + 59*x^5 + 42*x^3 + 112*x^2 + 9*x + 32, x^93 + 74*x^91 + 51*x^89 + 80*x^88 + 68*x^87 + 97*x^85 + 96*x^84 + 102*x^83 + 91*x^81 + 112*x^80 + 24*x^79 + 111*x^77 + 64*x^76 + 62*x^75 + 13*x^73 + 112*x^72 + 116*x^71 + 103*x^69 + 96*x^68 + 114*x^67 + 45*x^65 + 80*x^64 + 32*x^63 + 106*x^61 + 4*x^59 + 94*x^57 + 32*x^56 + 72*x^55 + 10*x^53 + 64*x^52 + 92*x^51 + 14*x^49 + 96*x^48 + 16*x^47 + 30*x^45 + 28*x^43 + 26*x^41 + 96*x^40 + 72*x^39 + 46*x^37 + 64*x^36 + 68*x^35 + 58*x^33 + 32*x^32 + 32*x^31 + 69*x^29 + 82*x^27 + 127*x^25 + 16*x^24 + 116*x^23 + 5*x^21 + 96*x^20 + 30*x^19 + 103*x^17 + 48*x^16 + 24*x^15 + 67*x^13 + 64*x^12 + 6*x^11 + 73*x^9 + 48*x^8 + 68*x^7 + 123*x^5 + 96*x^4 + 106*x^3 + 73*x + 16, x^93 + 74*x^91 + 84*x^90 + 43*x^89 + 4*x^88 + 36*x^87 + 56*x^86 + 81*x^85 + 56*x^84 + 70*x^83 + 92*x^82 + 35*x^81 + 12*x^80 + 88*x^79 + 16*x^78 + 15*x^77 + 16*x^76 + 126*x^75 + 92*x^74 + 117*x^73 + 44*x^72 + 84*x^71 + 24*x^70 + 23*x^69 + 24*x^68 + 82*x^67 + 116*x^66 + 5*x^65 + 68*x^64 + 32*x^63 + 64*x^62 + 106*x^61 + 64*x^60 + 4*x^59 + 8*x^58 + 14*x^57 + 104*x^56 + 8*x^55 + 112*x^54 + 106*x^53 + 112*x^52 + 28*x^51 + 88*x^50 + 94*x^49 + 56*x^48 + 16*x^47 + 96*x^46 + 94*x^45 + 96*x^44 + 28*x^43 + 120*x^42 + 106*x^41 + 24*x^40 + 8*x^39 + 112*x^38 + 14*x^37 + 112*x^36 + 4*x^35 + 40*x^34 + 106*x^33 + 72*x^32 + 32*x^31 + 64*x^30 + 69*x^29 + 64*x^28 + 82*x^27 + 100*x^26 + 87*x^25 + 84*x^24 + 84*x^23 + 88*x^22 + 53*x^21 + 88*x^20 + 126*x^19 + 12*x^18 + 79*x^17 + 124*x^16 + 88*x^15 + 16*x^14 + 99*x^13 + 16*x^12 + 70*x^11 + 108*x^10 + 17*x^9 + 124*x^8 + 36*x^7 + 120*x^6 + 107*x^5 + 120*x^4 + 74*x^3 + 36*x^2 + 65*x + 52}


In [11]:
# check Lemma 5.6
def lem56Polynomials():
	R.<x>=PolynomialRing(QQ)
	ll2=getCoeffsWeaklyType2(7,[1,-135,7800])
	llshift2=[R(list(reversed(l)))(x+1) for l in ll2]
	lllist2=[list(reversed(l.coefficients(sparse=False))) for l in llshift2]
	return listPowerReduceOddPC(lllist2,(x+5)^75*(x-19)^13,scc957,7)

def checkLemma56():
	R.<x>=PolynomialRing(QQ)
	print "--- Candidates for char poly corresponding to 95 lines ---"
	print ""
	tic = time.time()
	cand95red=lem56Polynomials()
	toc = time.time()
	print "Time taken to compute char poly candidates: " + str(toc-tic) + " seconds"
	print ""
	print "Candidates for char poly:"
	for i in range(len(cand95red)):
		ff=R(list(reversed(cand95red[i])))*(x+5)^75*(x-19)^13
		ms=R(ff/gcd(ff,ff.derivative()))
		print i+1, factor(ff)
	print ""
	cand95=[cand95red[i] for i in [1,4,2,3,5,6]]
	FarkasCertificates=[
	[49420,889549,0,0,14218410144],
	[26657,479808,0,0,7099110312],
	[-2190,-9058, 0, 0, 0], 
	[44780,443285, 2488265, 0, 0, 0],
	[15690, 266716, 0, 0, 3568395060],
	[-2587,-10412, 0, 0, 0]
	]
	bag=[]
	for i in range(len(cand95)):
		ff=R(list(reversed(cand95[i])))*(x+5)^75*(x-19)^13
		ms=R(ff/gcd(ff,ff.derivative()))
		g=R(ff.derivative()/gcd(ff,ff.derivative()))
		deg=ms.degree()
		f=ms+94*x^(deg-2)
		coeffs=list(reversed(f.coefficients(sparse=False)))
		gf=x^(deg-3)*R([coeffs[2],coeffs[1],coeffs[0]])
		ggf=gf(x-1)
		clist=list(reversed(ggf.coefficients(sparse=False)))
		print "------- Infeasibility of " + str(factor(ff)) + " -------"
		print ""
		tic = time.time()
		ll=getCoeffsType2(deg-1,[clist[0],clist[1],clist[2]])
		llpol=[R(list(reversed(l)))(x+1) for l in ll]
		ll2=[list(reversed(l.coefficients(sparse=False))) for l in llpol]
		bag+=[[factor(ff),listInterlaceReduce(ll2,ms)]]
		toc = time.time()
		print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
		print ""
		deg=ms.degree()
		numrows=len(bag[i][1])
		m=matrix(numrows,deg,[bag[i][1][j] for j in range(numrows)])
		gg=vector(list(reversed(g.coefficients(sparse=False))))
		print "Coefficient matrix A for interlacing char polys:"
		print m
		print ""
		mm=vector(list(reversed(FarkasCertificates[i])))
		print "Certificate of infeasibility c:"
		print "c = " + str(mm)
		ac=mm*m.transpose()
		print "Ac >= 0: " + str(isAtLeastZero(ac))
		print "Ac = " + str(ac)
		innerprod=sum([gg[j]*mm[j] for j in range(deg)])
		print "<g,c> < 0: " + str(innerprod < 0)
		print "<g,c> = " + str(innerprod)
		print ""


# check Lemma 5.7
# (x + 5)^56*(x-13)^4*(x-15)^14*(x-18)
def lem57InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll2=getCoeffsType2(3,[1,-56,1028])
	llshift2=[R(list(reversed(l)))(x+1) for l in ll2]
	lllist2=[list(reversed(l.coefficients(sparse=False))) for l in llshift2]
	llred2=listInterlaceReduce(lllist2,(x+5)*(x-17)*(x-19)*(x-22))
	return listPowerReduce(llred2,(x+5)^74*(x-17)^3*(x-19)^14)

def checkLemma57Part1():
	R.<x>=PolynomialRing(QQ)
	tic = time.time()
	llSeidelred=lem57InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	print "Interlacing characteristic polynomials:"
	for i in range(len(llSeidelred)):
		ff=R(list(reversed(llSeidelred[i])))*(x+5)^74*(x-17)^3*(x-19)^14
		ms=R(ff/gcd(ff,ff.derivative()))
		print i+1, factor(ff)
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,4,[llSeidelred[j] for j in range(numrows)])
	mults=vector([75,4,15,1])
	froots=[-5,17,19,22]
	f=prod([(x-r) for r in froots])
	fbas=[R(f/(x-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(4,4,[fbaslist[j] for j in range(4)])
	bb=mults*fbasm
	#submatrix of m without f1
	mf1=m[range(1,numrows),range(4)]
	print "Matrix A' corresponding to interlacing polynomials without f1:" 
	print mf1
	print "" 
	#Farkas certificate 
	fc1=vector(list(reversed([917,0,0,4776043])))
	print "Certificate of warranty c:"
	print "c = " + str(fc1)  
	ac = fc1*mf1.transpose()
	print "Ac >= 0: " + str(isAtLeastZero(ac))
	print "Ac = " + str(ac)
	innerprod = sum([fc1[j]*bb[j] for j in range(4)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)


def lem57InterlacingCharacteristicPolynomials2():
	R.<x>=PolynomialRing(QQ)
	ll2=getCoeffsWeaklyType2(5,[1,-89,3144])
	llshift2=[R(list(reversed(l)))(x+1) for l in ll2]
	lllist2=[list(reversed(l.coefficients(sparse=False))) for l in llshift2]
	llred2=listInterlaceReduce(lllist2,(x+5)*(x-17)*(x-19)*(x^3-53*x^2+919*x-5211))
	return listPowerReduceOddPC(llred2,(x+5)^73*(x-17)^2*(x-19)^13,scc937,7)

def checkLemma57Part2():
	R.<x>=PolynomialRing(QQ)
	tic = time.time()
	llSeidelred=lem57InterlacingCharacteristicPolynomials2()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	print "Interlacing characteristic polynomials:"
	for i in range(len(llSeidelred)):
		ff=R(list(reversed(llSeidelred[i])))*(x+5)^74*(x-17)^2*(x-19)^13
		ms=R(ff/gcd(ff,ff.derivative()))
		print i+1, factor(ff)
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,6,[llSeidelred[j] for j in range(numrows)])
	mults=vector([74,3,14,1,1,1])
	N.<al>=NumberField(x^3-53*x^2 + 919*x -5211)
	N1.<z>=PolynomialRing(N)
	N2.<be>=NumberField(z^2 + (al - 53)*z + al^2 - 53*al + 919)
	NN.<zz>=PolynomialRing(N2)
	froots=[-5,17,19,al,be,53-al-be]
	f=prod([(z-r) for r in froots])
	fbas=[NN(f/(z-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(6,6,[fbaslist[j] for j in range(6)])
	bb=mults*fbasm
	print "Coefficient matrix A for interlacing char polys:"
	print m
	print ""
	#Farkas certificate 
	fc1=vector(list(reversed([265131,4595613,79981334,0,0,2282735504746])))  
	print "Certificate of infeasibility c:"
	print "c = " + str(fc1)  
	ac = fc1*m.transpose()
	print "Ac >= 0: " + str(isAtLeastZero(ac))
	print "Ac = " + str(ac)
	innerprod = sum([fc1[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(RR(innerprod) < 0)
	print "<g,c> = " + str(innerprod)

def checkLemma57():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x + 5)^75*(x-17)^4*(x-19)^15*(x-22))) + "  ---"
	print ""
	checkLemma57Part1()
	print ""
	print "--- Infeasibility of f1 ---"
	print ""
	checkLemma57Part2()

In [12]:
#precompute Seidel char polys classes n=29, e=7
#scc297=SeidelCharPolysMod(29,7)

In [13]:
scc297={x^29 + 106*x^27 + 96*x^26 + 3*x^25 + 16*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 86*x^19 + 32*x^18 + 51*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + x^9 + 112*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 10*x^3 + 96*x^2 + 73*x + 80, x^29 + 106*x^27 + 28*x^26 + 43*x^25 + 60*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 84*x^18 + 11*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 89*x^9 + 36*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 12*x^2 + 113*x + 12, x^29 + 106*x^27 + 4*x^26 + 123*x^25 + 84*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 76*x^18 + 123*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 9*x^9 + 76*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 84*x^2 + x + 4, x^29 + 106*x^27 + 100*x^26 + 11*x^25 + 36*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 44*x^18 + 43*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 121*x^9 + 124*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 116*x^2 + 81*x + 84, x^29 + 106*x^27 + 120*x^26 + 99*x^25 + 104*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 104*x^18 + 19*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 33*x^9 + 88*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 88*x^2 + 105*x + 72, x^29 + 106*x^27 + 12*x^26 + 27*x^25 + 60*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 100*x^18 + 91*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 105*x^9 + 36*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 124*x^2 + 33*x + 76, x^29 + 106*x^27 + 12*x^26 + 59*x^25 + 60*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 100*x^18 + 59*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 73*x^9 + 36*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 124*x^2 + 65*x + 76, x^29 + 106*x^27 + 96*x^26 + 51*x^25 + 32*x^24 + 36*x^23 + 121*x^21 + 86*x^19 + 96*x^18 + 67*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 81*x^9 + 96*x^8 + 36*x^7 + 107*x^5 + 10*x^3 + 32*x^2 + 57*x + 96, x^29 + 106*x^27 + 60*x^26 + 59*x^25 + 12*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 116*x^18 + 59*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 73*x^9 + 84*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 108*x^2 + 65*x + 92, x^29 + 106*x^27 + 64*x^26 + 51*x^25 + 32*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 86*x^19 + 67*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 81*x^9 + 96*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 10*x^3 + 57*x + 96, x^29 + 106*x^27 + 24*x^26 + 99*x^25 + 104*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 72*x^18 + 19*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 33*x^9 + 88*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 120*x^2 + 105*x + 72, x^29 + 106*x^27 + 20*x^26 + 11*x^25 + 116*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 124*x^18 + 107*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 121*x^9 + 44*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 36*x^2 + 17*x + 36, x^29 + 106*x^27 + 51*x^25 + 32*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 86*x^19 + 64*x^18 + 67*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 81*x^9 + 96*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 10*x^3 + 64*x^2 + 57*x + 96, x^29 + 106*x^27 + 88*x^26 + 115*x^25 + 56*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 8*x^18 + 3*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 17*x^9 + 8*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 56*x^2 + 121*x + 88, x^29 + 106*x^27 + 28*x^26 + 43*x^25 + 92*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 20*x^18 + 75*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 89*x^9 + 4*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 76*x^2 + 49*x + 108, x^29 + 106*x^27 + 24*x^26 + 67*x^25 + 72*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 8*x^18 + 115*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 65*x^9 + 120*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 56*x^2 + 9*x + 104, x^29 + 106*x^27 + 120*x^26 + 3*x^25 + 8*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 104*x^18 + 115*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + x^9 + 56*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 88*x^2 + 9*x + 104, x^29 + 106*x^27 + 96*x^26 + 99*x^25 + 80*x^24 + 100*x^23 + 89*x^21 + 32*x^20 + 22*x^19 + 96*x^18 + 19*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 33*x^9 + 48*x^8 + 100*x^7 + 75*x^5 + 32*x^4 + 74*x^3 + 32*x^2 + 105*x + 80, x^29 + 106*x^27 + 48*x^26 + 83*x^25 + 48*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 80*x^18 + 35*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 49*x^9 + 80*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 48*x^2 + 89*x + 48, x^29 + 106*x^27 + 51*x^25 + 96*x^24 + 100*x^23 + 57*x^21 + 64*x^20 + 22*x^19 + 3*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 81*x^9 + 32*x^8 + 100*x^7 + 43*x^5 + 64*x^4 + 74*x^3 + 121*x + 96, x^29 + 106*x^27 + 44*x^26 + 27*x^25 + 124*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 68*x^18 + 91*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 105*x^9 + 100*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 28*x^2 + 33*x + 12, x^29 + 106*x^27 + 64*x^26 + 99*x^25 + 80*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 22*x^19 + 19*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 33*x^9 + 48*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 74*x^3 + 105*x + 80, x^29 + 106*x^27 + 28*x^26 + 59*x^25 + 44*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 84*x^18 + 123*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 73*x^9 + 52*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 12*x^2 + x + 60, x^29 + 106*x^27 + 48*x^26 + 35*x^25 + 64*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 80*x^18 + 83*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 97*x^9 + 64*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 48*x^2 + 41*x, x^29 + 106*x^27 + 44*x^26 + 11*x^25 + 44*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 68*x^18 + 107*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 121*x^9 + 52*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 28*x^2 + 17*x + 124, x^29 + 106*x^27 + 20*x^26 + 43*x^25 + 84*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 124*x^18 + 75*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 89*x^9 + 76*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 36*x^2 + 49*x + 4, x^29 + 106*x^27 + 99*x^25 + 80*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 22*x^19 + 64*x^18 + 19*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 33*x^9 + 48*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 74*x^3 + 64*x^2 + 105*x + 80, x^29 + 106*x^27 + 108*x^26 + 27*x^25 + 60*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 4*x^18 + 91*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 105*x^9 + 36*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 92*x^2 + 33*x + 76, x^29 + 106*x^27 + 52*x^26 + 107*x^25 + 20*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 28*x^18 + 75*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 25*x^9 + 12*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 4*x^2 + 49*x + 4, x^29 + 106*x^27 + 108*x^26 + 107*x^25 + 108*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 68*x^18 + 75*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 25*x^9 + 116*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 28*x^2 + 49*x + 124, x^29 + 106*x^27 + 96*x^26 + 51*x^25 + 64*x^24 + 36*x^23 + 121*x^21 + 64*x^20 + 86*x^19 + 96*x^18 + 67*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 81*x^9 + 64*x^8 + 36*x^7 + 107*x^5 + 64*x^4 + 10*x^3 + 32*x^2 + 57*x, x^29 + 106*x^27 + 72*x^26 + 19*x^25 + 40*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 88*x^18 + 99*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 113*x^9 + 24*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 104*x^2 + 25*x + 8, x^29 + 106*x^27 + 88*x^26 + 83*x^25 + 120*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 8*x^18 + 35*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 49*x^9 + 72*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 56*x^2 + 89*x + 24, x^29 + 106*x^27 + 28*x^26 + 107*x^25 + 124*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 84*x^18 + 75*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 25*x^9 + 100*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 12*x^2 + 49*x + 76, x^29 + 106*x^27 + 76*x^26 + 59*x^25 + 92*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 100*x^18 + 123*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 73*x^9 + 4*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 124*x^2 + x + 44, x^29 + 106*x^27 + 20*x^26 + 27*x^25 + 36*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 124*x^18 + 91*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 105*x^9 + 124*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 36*x^2 + 33*x + 20, x^29 + 106*x^27 + 44*x^26 + 43*x^25 + 12*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 68*x^18 + 75*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 89*x^9 + 84*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 28*x^2 + 49*x + 92, x^29 + 106*x^27 + 52*x^26 + 123*x^25 + 36*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 92*x^18 + 123*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 9*x^9 + 124*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 68*x^2 + x + 20, x^29 + 106*x^27 + 80*x^26 + 35*x^25 + 100*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 48*x^18 + 83*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 97*x^9 + 100*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 80*x^2 + 41*x + 64, x^29 + 106*x^27 + 100*x^26 + 59*x^25 + 116*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 108*x^18 + 59*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 73*x^9 + 44*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 52*x^2 + 65*x + 36, x^29 + 106*x^27 + 88*x^26 + 83*x^25 + 24*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 72*x^18 + 99*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 49*x^9 + 40*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 120*x^2 + 25*x + 120, x^29 + 106*x^27 + 92*x^26 + 75*x^25 + 28*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 84*x^18 + 43*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 57*x^9 + 68*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 12*x^2 + 81*x + 44, x^29 + 106*x^27 + 32*x^26 + 51*x^25 + 32*x^24 + 36*x^23 + 121*x^21 + 86*x^19 + 32*x^18 + 67*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 81*x^9 + 96*x^8 + 36*x^7 + 107*x^5 + 10*x^3 + 96*x^2 + 57*x + 96, x^29 + 106*x^27 + 24*x^26 + 115*x^25 + 120*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 72*x^18 + 3*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 17*x^9 + 72*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 120*x^2 + 121*x + 24, x^29 + 106*x^27 + 100*x^26 + 75*x^25 + 68*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 44*x^18 + 107*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 57*x^9 + 92*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 116*x^2 + 17*x + 116, x^29 + 106*x^27 + 32*x^26 + 99*x^25 + 16*x^24 + 100*x^23 + 89*x^21 + 32*x^20 + 22*x^19 + 32*x^18 + 19*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 33*x^9 + 112*x^8 + 100*x^7 + 75*x^5 + 32*x^4 + 74*x^3 + 96*x^2 + 105*x + 16, x^29 + 106*x^27 + 84*x^26 + 27*x^25 + 36*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 60*x^18 + 91*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 105*x^9 + 124*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 100*x^2 + 33*x + 20, x^29 + 106*x^27 + 76*x^26 + 123*x^25 + 124*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 100*x^18 + 59*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 9*x^9 + 100*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 124*x^2 + 65*x + 76, x^29 + 106*x^27 + 12*x^26 + 59*x^25 + 124*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 36*x^18 + 123*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 73*x^9 + 100*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 60*x^2 + x + 76, x^29 + 106*x^27 + 64*x^26 + 99*x^25 + 16*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 22*x^19 + 19*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 33*x^9 + 112*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 74*x^3 + 105*x + 16, x^29 + 106*x^27 + 60*x^26 + 91*x^25 + 12*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 116*x^18 + 27*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 41*x^9 + 84*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 108*x^2 + 97*x + 92, x^29 + 106*x^27 + 64*x^26 + 83*x^25 + 100*x^23 + 121*x^21 + 22*x^19 + 64*x^18 + 99*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 49*x^9 + 100*x^7 + 107*x^5 + 74*x^3 + 64*x^2 + 25*x, x^29 + 106*x^27 + 28*x^26 + 59*x^25 + 12*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 84*x^18 + 123*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 73*x^9 + 84*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 12*x^2 + x + 28, x^29 + 106*x^27 + 12*x^26 + 107*x^25 + 44*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 36*x^18 + 75*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 25*x^9 + 52*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 60*x^2 + 49*x + 60, x^29 + 106*x^27 + 8*x^26 + 83*x^25 + 8*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 88*x^18 + 99*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 49*x^9 + 56*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 104*x^2 + 25*x + 40, x^29 + 106*x^27 + 80*x^26 + 115*x^25 + 16*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 48*x^18 + 3*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 17*x^9 + 112*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 80*x^2 + 121*x + 16, x^29 + 106*x^27 + 32*x^26 + 3*x^25 + 80*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 86*x^19 + 96*x^18 + 51*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + x^9 + 48*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 10*x^3 + 32*x^2 + 73*x + 16, x^29 + 106*x^27 + 99*x^25 + 16*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 22*x^19 + 64*x^18 + 19*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 33*x^9 + 112*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 74*x^3 + 64*x^2 + 105*x + 16, x^29 + 106*x^27 + 36*x^26 + 27*x^25 + 84*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 108*x^18 + 27*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 105*x^9 + 76*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 52*x^2 + 97*x + 68, x^29 + 106*x^27 + 4*x^26 + 75*x^25 + 4*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 76*x^18 + 43*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 57*x^9 + 28*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 84*x^2 + 81*x + 116, x^29 + 106*x^27 + 88*x^26 + 83*x^25 + 56*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 8*x^18 + 35*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 49*x^9 + 8*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 56*x^2 + 89*x + 88, x^29 + 106*x^27 + 52*x^26 + 59*x^25 + 68*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 92*x^18 + 59*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 73*x^9 + 92*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 68*x^2 + 65*x + 52, x^29 + 106*x^27 + 32*x^26 + 99*x^25 + 48*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 86*x^19 + 96*x^18 + 83*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 33*x^9 + 80*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 10*x^3 + 32*x^2 + 41*x + 112, x^29 + 106*x^27 + 24*x^26 + 67*x^25 + 104*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 8*x^18 + 115*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 65*x^9 + 88*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 56*x^2 + 9*x + 8, x^29 + 106*x^27 + 83*x^25 + 100*x^23 + 121*x^21 + 22*x^19 + 99*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 49*x^9 + 100*x^7 + 107*x^5 + 74*x^3 + 25*x, x^29 + 106*x^27 + 60*x^26 + 43*x^25 + 124*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 116*x^18 + 75*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 89*x^9 + 100*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 108*x^2 + 49*x + 12, x^29 + 106*x^27 + 108*x^26 + 75*x^25 + 76*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 4*x^18 + 43*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 57*x^9 + 20*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 92*x^2 + 81*x + 28, x^29 + 106*x^27 + 72*x^26 + 35*x^25 + 56*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 24*x^18 + 19*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 97*x^9 + 8*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 40*x^2 + 105*x + 24, x^29 + 106*x^27 + 80*x^26 + 51*x^25 + 16*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 112*x^18 + 3*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 81*x^9 + 112*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 16*x^2 + 121*x + 80, x^29 + 106*x^27 + 20*x^26 + 75*x^25 + 116*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 124*x^18 + 43*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 57*x^9 + 44*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 36*x^2 + 81*x + 36, x^29 + 106*x^27 + 52*x^26 + 59*x^25 + 100*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 92*x^18 + 59*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 73*x^9 + 60*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 68*x^2 + 65*x + 84, x^29 + 106*x^27 + 44*x^26 + 11*x^25 + 108*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 68*x^18 + 107*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 121*x^9 + 116*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 28*x^2 + 17*x + 60, x^29 + 106*x^27 + 68*x^26 + 75*x^25 + 68*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 76*x^18 + 107*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 57*x^9 + 92*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 84*x^2 + 17*x + 116, x^29 + 106*x^27 + 60*x^26 + 123*x^25 + 12*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 116*x^18 + 123*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 9*x^9 + 84*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 108*x^2 + x + 92, x^29 + 106*x^27 + 16*x^26 + 35*x^25 + 96*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 48*x^18 + 19*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 97*x^9 + 32*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 80*x^2 + 105*x + 96, x^29 + 106*x^27 + 124*x^26 + 59*x^25 + 108*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 116*x^18 + 123*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 73*x^9 + 116*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 108*x^2 + x + 124, x^29 + 106*x^27 + 72*x^26 + 99*x^25 + 88*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 88*x^18 + 19*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 33*x^9 + 104*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 104*x^2 + 105*x + 120, x^29 + 106*x^27 + 68*x^26 + 11*x^25 + 100*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 12*x^18 + 107*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 121*x^9 + 60*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 20*x^2 + 17*x + 84, x^29 + 106*x^27 + 52*x^26 + 107*x^25 + 84*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 92*x^18 + 11*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 25*x^9 + 76*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 68*x^2 + 113*x + 4, x^29 + 106*x^27 + 16*x^26 + 83*x^25 + 48*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 48*x^18 + 99*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 49*x^9 + 80*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 80*x^2 + 25*x + 112, x^29 + 106*x^27 + 40*x^26 + 83*x^25 + 40*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 56*x^18 + 99*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 49*x^9 + 24*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 8*x^2 + 25*x + 72, x^29 + 106*x^27 + 28*x^26 + 11*x^25 + 60*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 84*x^18 + 43*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 121*x^9 + 36*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 12*x^2 + 81*x + 12, x^29 + 106*x^27 + 56*x^26 + 51*x^25 + 120*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 40*x^18 + 67*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 81*x^9 + 72*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 24*x^2 + 57*x + 24, x^29 + 106*x^27 + 64*x^26 + 19*x^25 + 96*x^24 + 100*x^23 + 121*x^21 + 64*x^20 + 22*x^19 + 64*x^18 + 35*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 113*x^9 + 32*x^8 + 100*x^7 + 107*x^5 + 64*x^4 + 74*x^3 + 64*x^2 + 89*x + 96, x^29 + 106*x^27 + 84*x^26 + 91*x^25 + 68*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 124*x^18 + 91*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 41*x^9 + 92*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 36*x^2 + 33*x + 116, x^29 + 106*x^27 + 36*x^26 + 75*x^25 + 100*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 44*x^18 + 43*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 57*x^9 + 60*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 116*x^2 + 81*x + 84, x^29 + 106*x^27 + 28*x^26 + 43*x^25 + 124*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 20*x^18 + 75*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 89*x^9 + 100*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 76*x^2 + 49*x + 12, x^29 + 106*x^27 + 115*x^25 + 100*x^23 + 57*x^21 + 22*x^19 + 67*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 17*x^9 + 100*x^7 + 43*x^5 + 74*x^3 + 57*x, x^29 + 106*x^27 + 92*x^26 + 75*x^25 + 28*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 20*x^18 + 107*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 57*x^9 + 68*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 76*x^2 + 17*x + 108, x^29 + 106*x^27 + 80*x^26 + 67*x^25 + 96*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 22*x^19 + 48*x^18 + 51*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 65*x^9 + 32*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 74*x^3 + 80*x^2 + 73*x + 32, x^29 + 106*x^27 + 80*x^26 + 19*x^25 + 80*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 48*x^18 + 99*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 113*x^9 + 48*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 80*x^2 + 25*x + 80, x^29 + 106*x^27 + 56*x^26 + 99*x^25 + 8*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 40*x^18 + 19*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 33*x^9 + 56*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 24*x^2 + 105*x + 104, x^29 + 106*x^27 + 48*x^26 + 3*x^25 + 64*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 86*x^19 + 16*x^18 + 51*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + x^9 + 64*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 10*x^3 + 112*x^2 + 73*x + 64, x^29 + 106*x^27 + 20*x^26 + 43*x^25 + 116*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 124*x^18 + 75*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 89*x^9 + 44*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 36*x^2 + 49*x + 36, x^29 + 106*x^27 + 48*x^26 + 67*x^25 + 36*x^23 + 32*x^22 + 89*x^21 + 86*x^19 + 16*x^18 + 115*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 65*x^9 + 36*x^7 + 32*x^6 + 75*x^5 + 10*x^3 + 112*x^2 + 9*x, x^29 + 106*x^27 + 24*x^26 + 35*x^25 + 8*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 72*x^18 + 83*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 97*x^9 + 56*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 120*x^2 + 41*x + 104, x^29 + 106*x^27 + 4*x^26 + 91*x^25 + 84*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 76*x^18 + 27*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 41*x^9 + 76*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 84*x^2 + 97*x + 4, x^29 + 106*x^27 + 48*x^26 + 83*x^25 + 80*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 80*x^18 + 35*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 49*x^9 + 48*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 48*x^2 + 89*x + 80, x^29 + 106*x^27 + 92*x^26 + 107*x^25 + 28*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 20*x^18 + 75*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 25*x^9 + 68*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 76*x^2 + 49*x + 108, x^29 + 106*x^27 + 28*x^26 + 59*x^25 + 12*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 20*x^18 + 59*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 73*x^9 + 84*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 76*x^2 + 65*x + 92, x^29 + 106*x^27 + 32*x^26 + 67*x^25 + 80*x^24 + 100*x^23 + 25*x^21 + 32*x^20 + 22*x^19 + 32*x^18 + 51*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 65*x^9 + 48*x^8 + 100*x^7 + 11*x^5 + 32*x^4 + 74*x^3 + 96*x^2 + 73*x + 80, x^29 + 106*x^27 + 64*x^26 + 67*x^25 + 80*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 22*x^19 + 51*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 65*x^9 + 48*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 74*x^3 + 73*x + 80, x^29 + 106*x^27 + 112*x^26 + 19*x^25 + 80*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 80*x^18 + 35*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 113*x^9 + 48*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 48*x^2 + 89*x + 16, x^29 + 106*x^27 + 76*x^26 + 107*x^25 + 44*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 36*x^18 + 11*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 25*x^9 + 52*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 60*x^2 + 113*x + 124, x^29 + 106*x^27 + 67*x^25 + 80*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 22*x^19 + 64*x^18 + 51*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 65*x^9 + 48*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 74*x^3 + 64*x^2 + 73*x + 80, x^29 + 106*x^27 + 84*x^26 + 11*x^25 + 84*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 60*x^18 + 107*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 121*x^9 + 76*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 100*x^2 + 17*x + 4, x^29 + 106*x^27 + 108*x^26 + 11*x^25 + 44*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 4*x^18 + 107*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 121*x^9 + 52*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 92*x^2 + 17*x + 124, x^29 + 106*x^27 + 96*x^26 + 83*x^25 + 32*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 22*x^19 + 32*x^18 + 99*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 49*x^9 + 96*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 74*x^3 + 96*x^2 + 25*x + 32, x^29 + 106*x^27 + 40*x^26 + 115*x^25 + 8*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 120*x^18 + 3*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 17*x^9 + 56*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 72*x^2 + 121*x + 104, x^29 + 106*x^27 + 64*x^26 + 51*x^25 + 36*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 86*x^19 + 67*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 81*x^9 + 36*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 10*x^3 + 57*x + 64, x^29 + 106*x^27 + 44*x^26 + 75*x^25 + 44*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 68*x^18 + 43*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 57*x^9 + 52*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 28*x^2 + 81*x + 124, x^29 + 106*x^27 + 32*x^26 + 99*x^25 + 80*x^24 + 100*x^23 + 89*x^21 + 32*x^20 + 22*x^19 + 32*x^18 + 19*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 33*x^9 + 48*x^8 + 100*x^7 + 75*x^5 + 32*x^4 + 74*x^3 + 96*x^2 + 105*x + 80, x^29 + 106*x^27 + 12*x^26 + 75*x^25 + 108*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 100*x^18 + 43*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 57*x^9 + 116*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 124*x^2 + 81*x + 60, x^29 + 106*x^27 + 64*x^26 + 115*x^25 + 96*x^24 + 100*x^23 + 57*x^21 + 64*x^20 + 22*x^19 + 64*x^18 + 67*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 17*x^9 + 32*x^8 + 100*x^7 + 43*x^5 + 64*x^4 + 74*x^3 + 64*x^2 + 57*x + 96, x^29 + 106*x^27 + 51*x^25 + 36*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 86*x^19 + 64*x^18 + 67*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 81*x^9 + 36*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 10*x^3 + 64*x^2 + 57*x + 64, x^29 + 106*x^27 + 120*x^26 + 3*x^25 + 104*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 104*x^18 + 115*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + x^9 + 88*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 88*x^2 + 9*x + 72, x^29 + 106*x^27 + 108*x^26 + 59*x^25 + 60*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 4*x^18 + 59*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 73*x^9 + 36*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 92*x^2 + 65*x + 76, x^29 + 106*x^27 + 108*x^26 + 11*x^25 + 12*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 4*x^18 + 107*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 121*x^9 + 84*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 92*x^2 + 17*x + 92, x^29 + 106*x^27 + 32*x^26 + 67*x^25 + 48*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 86*x^19 + 96*x^18 + 115*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 65*x^9 + 80*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 10*x^3 + 32*x^2 + 9*x + 112, x^29 + 106*x^27 + 4*x^26 + 43*x^25 + 100*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 12*x^18 + 11*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 89*x^9 + 60*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 20*x^2 + 113*x + 20, x^29 + 106*x^27 + 100*x^26 + 123*x^25 + 52*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 44*x^18 + 59*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 9*x^9 + 108*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 116*x^2 + 65*x + 36, x^29 + 106*x^27 + 8*x^26 + 67*x^25 + 88*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 24*x^18 + 51*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 65*x^9 + 104*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 40*x^2 + 73*x + 120, x^29 + 106*x^27 + 112*x^26 + 19*x^25 + 48*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 80*x^18 + 35*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 113*x^9 + 80*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 48*x^2 + 89*x + 112, x^29 + 106*x^27 + 120*x^26 + 51*x^25 + 56*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 104*x^18 + 67*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 81*x^9 + 8*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 88*x^2 + 57*x + 88, x^29 + 106*x^27 + 28*x^26 + 43*x^25 + 28*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 84*x^18 + 11*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 89*x^9 + 68*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 12*x^2 + 113*x + 108, x^29 + 106*x^27 + 116*x^26 + 107*x^25 + 84*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 28*x^18 + 11*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 25*x^9 + 76*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 4*x^2 + 113*x + 4, x^29 + 106*x^27 + 24*x^26 + 67*x^25 + 40*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 8*x^18 + 115*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 65*x^9 + 24*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 56*x^2 + 9*x + 72, x^29 + 106*x^27 + 112*x^26 + 35*x^25 + 64*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 16*x^18 + 83*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 97*x^9 + 64*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 112*x^2 + 41*x, x^29 + 106*x^27 + 88*x^26 + 67*x^25 + 8*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 72*x^18 + 115*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 65*x^9 + 56*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 120*x^2 + 9*x + 40, x^29 + 106*x^27 + 64*x^26 + 99*x^25 + 80*x^24 + 36*x^23 + 25*x^21 + 96*x^20 + 86*x^19 + 64*x^18 + 83*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 33*x^9 + 48*x^8 + 36*x^7 + 11*x^5 + 96*x^4 + 10*x^3 + 64*x^2 + 41*x + 16, x^29 + 106*x^27 + 92*x^26 + 91*x^25 + 12*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 84*x^18 + 27*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 41*x^9 + 84*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 12*x^2 + 97*x + 92, x^29 + 106*x^27 + 64*x^26 + 3*x^25 + 80*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 22*x^19 + 115*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + x^9 + 48*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 74*x^3 + 9*x + 80, x^29 + 106*x^27 + 28*x^26 + 91*x^25 + 44*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 20*x^18 + 27*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 41*x^9 + 52*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 76*x^2 + 97*x + 124, x^29 + 106*x^27 + 24*x^26 + 83*x^25 + 56*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 72*x^18 + 35*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 49*x^9 + 8*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 120*x^2 + 89*x + 88, x^29 + 106*x^27 + 64*x^26 + 67*x^25 + 48*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 22*x^19 + 51*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 65*x^9 + 80*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 74*x^3 + 73*x + 48, x^29 + 106*x^27 + 3*x^25 + 80*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 22*x^19 + 64*x^18 + 115*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + x^9 + 48*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 74*x^3 + 64*x^2 + 9*x + 80, x^29 + 106*x^27 + 40*x^26 + 35*x^25 + 88*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 56*x^18 + 19*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 97*x^9 + 104*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 8*x^2 + 105*x + 56, x^29 + 106*x^27 + 32*x^26 + 115*x^25 + 32*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 22*x^19 + 96*x^18 + 67*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 17*x^9 + 96*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 74*x^3 + 32*x^2 + 57*x + 32, x^29 + 106*x^27 + 68*x^26 + 11*x^25 + 100*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 76*x^18 + 43*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 121*x^9 + 60*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 84*x^2 + 81*x + 20, x^29 + 106*x^27 + 120*x^26 + 99*x^25 + 40*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 40*x^18 + 83*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 33*x^9 + 24*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 24*x^2 + 41*x + 72, x^29 + 106*x^27 + 36*x^26 + 123*x^25 + 84*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 108*x^18 + 59*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 9*x^9 + 76*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 52*x^2 + 65*x + 68, x^29 + 106*x^27 + 28*x^26 + 107*x^25 + 124*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 20*x^18 + 11*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 25*x^9 + 100*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 76*x^2 + 113*x + 12, x^29 + 106*x^27 + 112*x^26 + 67*x^25 + 32*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 80*x^18 + 115*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 65*x^9 + 96*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 48*x^2 + 9*x + 32, x^29 + 106*x^27 + 24*x^26 + 19*x^25 + 56*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 72*x^18 + 99*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 113*x^9 + 8*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 120*x^2 + 25*x + 88, x^29 + 106*x^27 + 8*x^26 + 3*x^25 + 56*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 88*x^18 + 51*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + x^9 + 8*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 104*x^2 + 73*x + 24, x^29 + 106*x^27 + 100*x^26 + 123*x^25 + 20*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 108*x^18 + 123*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 9*x^9 + 12*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 52*x^2 + x + 68, x^29 + 106*x^27 + 40*x^26 + 67*x^25 + 120*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 120*x^18 + 51*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 65*x^9 + 72*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 72*x^2 + 73*x + 24, x^29 + 106*x^27 + 44*x^26 + 59*x^25 + 28*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 4*x^18 + 123*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 73*x^9 + 68*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 92*x^2 + x + 108, x^29 + 106*x^27 + 48*x^26 + 35*x^25 + 32*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 22*x^19 + 80*x^18 + 83*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 97*x^9 + 96*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 74*x^3 + 48*x^2 + 41*x + 96, x^29 + 106*x^27 + 108*x^26 + 43*x^25 + 76*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 4*x^18 + 75*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 89*x^9 + 20*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 92*x^2 + 49*x + 28, x^29 + 106*x^27 + 76*x^26 + 123*x^25 + 124*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 36*x^18 + 123*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 9*x^9 + 100*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 60*x^2 + x + 12, x^29 + 106*x^27 + 52*x^26 + 27*x^25 + 36*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 92*x^18 + 91*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 105*x^9 + 124*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 68*x^2 + 33*x + 20, x^29 + 106*x^27 + 72*x^26 + 83*x^25 + 8*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 88*x^18 + 35*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 49*x^9 + 56*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 104*x^2 + 89*x + 104, x^29 + 106*x^27 + 68*x^26 + 123*x^25 + 52*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 76*x^18 + 59*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 9*x^9 + 108*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 84*x^2 + 65*x + 36, x^29 + 106*x^27 + 24*x^26 + 115*x^25 + 24*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 72*x^18 + 3*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 17*x^9 + 40*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 120*x^2 + 121*x + 56, x^29 + 106*x^27 + 20*x^26 + 43*x^25 + 84*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 60*x^18 + 11*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 89*x^9 + 76*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 100*x^2 + 113*x + 68, x^29 + 106*x^27 + 28*x^26 + 123*x^25 + 12*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 84*x^18 + 59*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 9*x^9 + 84*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 12*x^2 + 65*x + 28, x^29 + 106*x^27 + 124*x^26 + 75*x^25 + 124*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 116*x^18 + 107*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 57*x^9 + 100*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 108*x^2 + 17*x + 76, x^29 + 106*x^27 + 108*x^26 + 91*x^25 + 28*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 68*x^18 + 91*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 41*x^9 + 68*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 28*x^2 + 33*x + 108, x^29 + 106*x^27 + 116*x^26 + 27*x^25 + 4*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 92*x^18 + 27*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 105*x^9 + 28*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 68*x^2 + 97*x + 52, x^29 + 106*x^27 + 44*x^26 + 27*x^25 + 28*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 4*x^18 + 27*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 105*x^9 + 68*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 92*x^2 + 97*x + 108, x^29 + 106*x^27 + 68*x^26 + 107*x^25 + 68*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 76*x^18 + 75*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 25*x^9 + 92*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 84*x^2 + 49*x + 116, x^29 + 106*x^27 + 32*x^26 + 3*x^25 + 16*x^24 + 100*x^23 + 25*x^21 + 32*x^20 + 22*x^19 + 32*x^18 + 115*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + x^9 + 112*x^8 + 100*x^7 + 11*x^5 + 32*x^4 + 74*x^3 + 96*x^2 + 9*x + 16, x^29 + 106*x^27 + 64*x^26 + 3*x^25 + 16*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 22*x^19 + 115*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + x^9 + 112*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 74*x^3 + 9*x + 16, x^29 + 106*x^27 + 76*x^26 + 11*x^25 + 76*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 36*x^18 + 107*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 121*x^9 + 20*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 60*x^2 + 17*x + 28, x^29 + 106*x^27 + 112*x^26 + 51*x^25 + 80*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 16*x^18 + 67*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 81*x^9 + 48*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 112*x^2 + 57*x + 80, x^29 + 106*x^27 + 100*x^26 + 107*x^25 + 4*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 44*x^18 + 75*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 25*x^9 + 28*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 116*x^2 + 49*x + 52, x^29 + 106*x^27 + 60*x^26 + 11*x^25 + 60*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 52*x^18 + 43*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 121*x^9 + 36*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 44*x^2 + 81*x + 12, x^29 + 106*x^27 + 60*x^26 + 59*x^25 + 108*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 52*x^18 + 123*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 73*x^9 + 116*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 44*x^2 + x + 124, x^29 + 106*x^27 + 3*x^25 + 16*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 22*x^19 + 64*x^18 + 115*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + x^9 + 112*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 74*x^3 + 64*x^2 + 9*x + 16, x^29 + 106*x^27 + 80*x^26 + 3*x^25 + 96*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 112*x^18 + 51*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + x^9 + 32*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 16*x^2 + 73*x + 96, x^29 + 106*x^27 + 28*x^26 + 75*x^25 + 92*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 20*x^18 + 43*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 57*x^9 + 4*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 76*x^2 + 81*x + 108, x^29 + 106*x^27 + 40*x^26 + 51*x^25 + 72*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 120*x^18 + 67*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 81*x^9 + 120*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 72*x^2 + 57*x + 40, x^29 + 106*x^27 + 28*x^26 + 107*x^25 + 60*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 84*x^18 + 75*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 25*x^9 + 36*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 12*x^2 + 49*x + 12, x^29 + 106*x^27 + 48*x^26 + 83*x^25 + 16*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 80*x^18 + 35*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 49*x^9 + 112*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 48*x^2 + 89*x + 16, x^29 + 106*x^27 + 120*x^26 + 35*x^25 + 104*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 104*x^18 + 83*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 97*x^9 + 88*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 88*x^2 + 41*x + 72, x^29 + 106*x^27 + 24*x^26 + 51*x^25 + 88*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 8*x^18 + 3*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 81*x^9 + 104*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 56*x^2 + 121*x + 56, x^29 + 106*x^27 + 108*x^26 + 123*x^25 + 60*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 68*x^18 + 59*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 9*x^9 + 36*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 28*x^2 + 65*x + 12, x^29 + 106*x^27 + 32*x^26 + 19*x^25 + 96*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 22*x^19 + 96*x^18 + 35*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 113*x^9 + 32*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 74*x^3 + 32*x^2 + 89*x + 96, x^29 + 106*x^27 + 88*x^26 + 19*x^25 + 56*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 8*x^18 + 99*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 113*x^9 + 8*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 56*x^2 + 25*x + 88, x^29 + 106*x^27 + 28*x^26 + 107*x^25 + 92*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 20*x^18 + 11*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 25*x^9 + 4*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 76*x^2 + 113*x + 108, x^29 + 106*x^27 + 120*x^26 + 99*x^25 + 8*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 40*x^18 + 83*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 33*x^9 + 56*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 24*x^2 + 41*x + 40, x^29 + 106*x^27 + 32*x^26 + 83*x^25 + 64*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 22*x^19 + 96*x^18 + 99*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 49*x^9 + 64*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 74*x^3 + 32*x^2 + 25*x + 64, x^29 + 106*x^27 + 92*x^26 + 11*x^25 + 60*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 20*x^18 + 43*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 121*x^9 + 36*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 76*x^2 + 81*x + 12, x^29 + 106*x^27 + 80*x^26 + 99*x^25 + 64*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 48*x^18 + 19*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 33*x^9 + 64*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 80*x^2 + 105*x, x^29 + 106*x^27 + 68*x^26 + 11*x^25 + 4*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 12*x^18 + 107*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 121*x^9 + 28*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 20*x^2 + 17*x + 116, x^29 + 106*x^27 + 32*x^26 + 35*x^25 + 80*x^24 + 100*x^23 + 89*x^21 + 32*x^20 + 22*x^19 + 32*x^18 + 83*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 97*x^9 + 48*x^8 + 100*x^7 + 75*x^5 + 32*x^4 + 74*x^3 + 96*x^2 + 41*x + 80, x^29 + 106*x^27 + 60*x^26 + 27*x^25 + 12*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 116*x^18 + 91*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 105*x^9 + 84*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 108*x^2 + 33*x + 92, x^29 + 106*x^27 + 64*x^26 + 35*x^25 + 80*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 22*x^19 + 83*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 97*x^9 + 48*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 74*x^3 + 41*x + 80, x^29 + 106*x^27 + 108*x^26 + 75*x^25 + 44*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 4*x^18 + 43*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 57*x^9 + 52*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 92*x^2 + 81*x + 124, x^29 + 106*x^27 + 35*x^25 + 80*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 22*x^19 + 64*x^18 + 83*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 97*x^9 + 48*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 74*x^3 + 64*x^2 + 41*x + 80, x^29 + 106*x^27 + 8*x^26 + 19*x^25 + 40*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 88*x^18 + 35*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 113*x^9 + 24*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 104*x^2 + 89*x + 72, x^29 + 106*x^27 + 52*x^26 + 43*x^25 + 84*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 28*x^18 + 11*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 89*x^9 + 76*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 4*x^2 + 113*x + 68, x^29 + 106*x^27 + 20*x^26 + 123*x^25 + 36*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 124*x^18 + 123*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 9*x^9 + 124*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 36*x^2 + x + 20, x^29 + 106*x^27 + 92*x^26 + 107*x^25 + 60*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 84*x^18 + 11*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 25*x^9 + 36*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 12*x^2 + 113*x + 76, x^29 + 106*x^27 + 108*x^26 + 91*x^25 + 124*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 68*x^18 + 91*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 41*x^9 + 100*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 28*x^2 + 33*x + 76, x^29 + 106*x^27 + 116*x^26 + 75*x^25 + 116*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 28*x^18 + 43*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 57*x^9 + 44*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 4*x^2 + 81*x + 36, x^29 + 106*x^27 + 88*x^26 + 3*x^25 + 8*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 72*x^18 + 51*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + x^9 + 56*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 120*x^2 + 73*x + 40, x^29 + 106*x^27 + 88*x^26 + 67*x^25 + 40*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 72*x^18 + 115*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 65*x^9 + 24*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 120*x^2 + 9*x + 72, x^29 + 106*x^27 + 124*x^26 + 75*x^25 + 92*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 52*x^18 + 43*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 57*x^9 + 4*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 44*x^2 + 81*x + 108, x^29 + 106*x^27 + 32*x^26 + 51*x^25 + 96*x^24 + 36*x^23 + 121*x^21 + 86*x^19 + 32*x^18 + 67*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 81*x^9 + 32*x^8 + 36*x^7 + 107*x^5 + 10*x^3 + 96*x^2 + 57*x + 32, x^29 + 106*x^27 + 44*x^26 + 107*x^25 + 12*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 68*x^18 + 11*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 25*x^9 + 84*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 28*x^2 + 113*x + 92, x^29 + 106*x^27 + 4*x^26 + 11*x^25 + 4*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 12*x^18 + 43*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 121*x^9 + 28*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 20*x^2 + 81*x + 52, x^29 + 106*x^27 + 64*x^26 + 51*x^25 + 96*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 86*x^19 + 67*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 81*x^9 + 32*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 10*x^3 + 57*x + 32, x^29 + 106*x^27 + 32*x^26 + 3*x^25 + 48*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 86*x^19 + 96*x^18 + 51*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + x^9 + 80*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 10*x^3 + 32*x^2 + 73*x + 112, x^29 + 106*x^27 + 40*x^26 + 35*x^25 + 120*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 56*x^18 + 19*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 97*x^9 + 72*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 8*x^2 + 105*x + 88, x^29 + 106*x^27 + 32*x^26 + 99*x^25 + 112*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 86*x^19 + 96*x^18 + 83*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 33*x^9 + 16*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 10*x^3 + 32*x^2 + 41*x + 48, x^29 + 106*x^27 + 51*x^25 + 96*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 86*x^19 + 64*x^18 + 67*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 81*x^9 + 32*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 10*x^3 + 64*x^2 + 57*x + 32, x^29 + 106*x^27 + 104*x^26 + 99*x^25 + 120*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 56*x^18 + 19*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 33*x^9 + 72*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 8*x^2 + 105*x + 24, x^29 + 106*x^27 + 36*x^26 + 91*x^25 + 20*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 44*x^18 + 27*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 41*x^9 + 12*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 116*x^2 + 97*x + 68, x^29 + 106*x^27 + 124*x^26 + 43*x^25 + 92*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 116*x^18 + 11*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 89*x^9 + 4*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 108*x^2 + 113*x + 44, x^29 + 106*x^27 + 12*x^26 + 91*x^25 + 92*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 100*x^18 + 27*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 41*x^9 + 4*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 124*x^2 + 97*x + 108, x^29 + 106*x^27 + 32*x^26 + 115*x^25 + 64*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 22*x^19 + 96*x^18 + 67*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 17*x^9 + 64*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 74*x^3 + 32*x^2 + 57*x + 64, x^29 + 106*x^27 + 24*x^26 + 3*x^25 + 40*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 8*x^18 + 51*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + x^9 + 24*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 56*x^2 + 73*x + 72, x^29 + 106*x^27 + 72*x^26 + 35*x^25 + 120*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 88*x^18 + 83*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 97*x^9 + 72*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 104*x^2 + 41*x + 24, x^29 + 106*x^27 + 96*x^26 + 35*x^25 + 16*x^24 + 100*x^23 + 89*x^21 + 32*x^20 + 22*x^19 + 96*x^18 + 83*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 97*x^9 + 112*x^8 + 100*x^7 + 75*x^5 + 32*x^4 + 74*x^3 + 32*x^2 + 41*x + 16, x^29 + 106*x^27 + 68*x^26 + 91*x^25 + 84*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 12*x^18 + 27*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 41*x^9 + 76*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 20*x^2 + 97*x + 4, x^29 + 106*x^27 + 51*x^25 + 32*x^24 + 100*x^23 + 57*x^21 + 64*x^20 + 22*x^19 + 3*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 81*x^9 + 96*x^8 + 100*x^7 + 43*x^5 + 64*x^4 + 74*x^3 + 121*x + 32, x^29 + 106*x^27 + 64*x^26 + 35*x^25 + 16*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 22*x^19 + 83*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 97*x^9 + 112*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 74*x^3 + 41*x + 16, x^29 + 106*x^27 + 28*x^26 + 123*x^25 + 76*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 84*x^18 + 59*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 9*x^9 + 20*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 12*x^2 + 65*x + 92, x^29 + 106*x^27 + 12*x^26 + 43*x^25 + 108*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 36*x^18 + 11*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 89*x^9 + 116*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 60*x^2 + 113*x + 124, x^29 + 106*x^27 + 60*x^26 + 59*x^25 + 44*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 116*x^18 + 59*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 73*x^9 + 52*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 108*x^2 + 65*x + 124, x^29 + 106*x^27 + 35*x^25 + 16*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 22*x^19 + 64*x^18 + 83*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 97*x^9 + 112*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 74*x^3 + 64*x^2 + 41*x + 16, x^29 + 106*x^27 + 56*x^26 + 99*x^25 + 40*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 40*x^18 + 19*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 33*x^9 + 24*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 24*x^2 + 105*x + 8, x^29 + 106*x^27 + 120*x^26 + 67*x^25 + 72*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 40*x^18 + 115*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 65*x^9 + 120*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 24*x^2 + 9*x + 104, x^29 + 106*x^27 + 4*x^26 + 75*x^25 + 36*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 76*x^18 + 43*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 57*x^9 + 124*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 84*x^2 + 81*x + 20, x^29 + 106*x^27 + 100*x^26 + 75*x^25 + 4*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 44*x^18 + 107*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 57*x^9 + 28*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 116*x^2 + 17*x + 52, x^29 + 106*x^27 + 32*x^26 + 3*x^25 + 112*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 86*x^19 + 96*x^18 + 51*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + x^9 + 16*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 10*x^3 + 32*x^2 + 73*x + 48, x^29 + 106*x^27 + 24*x^26 + 19*x^25 + 24*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 8*x^18 + 35*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 113*x^9 + 40*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 56*x^2 + 89*x + 120, x^29 + 106*x^27 + 24*x^26 + 35*x^25 + 40*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 72*x^18 + 83*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 97*x^9 + 24*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 120*x^2 + 41*x + 8, x^29 + 106*x^27 + 80*x^26 + 51*x^25 + 80*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 112*x^18 + 3*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 81*x^9 + 48*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 16*x^2 + 121*x + 16, x^29 + 106*x^27 + 112*x^26 + 3*x^25 + 32*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 80*x^18 + 51*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + x^9 + 96*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 48*x^2 + 73*x + 32, x^29 + 106*x^27 + 12*x^26 + 43*x^25 + 76*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 100*x^18 + 75*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 89*x^9 + 20*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 124*x^2 + 49*x + 28, x^29 + 106*x^27 + 76*x^26 + 59*x^25 + 124*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 36*x^18 + 59*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 73*x^9 + 100*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 60*x^2 + 65*x + 12, x^29 + 106*x^27 + 19*x^25 + 32*x^24 + 100*x^23 + 121*x^21 + 64*x^20 + 22*x^19 + 35*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 113*x^9 + 96*x^8 + 100*x^7 + 107*x^5 + 64*x^4 + 74*x^3 + 89*x + 32, x^29 + 106*x^27 + 72*x^26 + 99*x^25 + 56*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 24*x^18 + 83*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 33*x^9 + 8*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 40*x^2 + 41*x + 24, x^29 + 106*x^27 + 4*x^26 + 123*x^25 + 84*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 12*x^18 + 59*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 9*x^9 + 76*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 20*x^2 + 65*x + 68, x^29 + 106*x^27 + 24*x^26 + 51*x^25 + 120*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 8*x^18 + 3*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 81*x^9 + 72*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 56*x^2 + 121*x + 88, x^29 + 106*x^27 + 100*x^26 + 27*x^25 + 116*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 108*x^18 + 91*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 105*x^9 + 44*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 52*x^2 + 33*x + 36, x^29 + 106*x^27 + 28*x^26 + 75*x^25 + 28*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 20*x^18 + 43*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 57*x^9 + 68*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 76*x^2 + 81*x + 44, x^29 + 106*x^27 + 60*x^26 + 59*x^25 + 108*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 116*x^18 + 59*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 73*x^9 + 116*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 108*x^2 + 65*x + 60, x^29 + 106*x^27 + 40*x^26 + 3*x^25 + 88*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 120*x^18 + 115*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + x^9 + 104*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 72*x^2 + 9*x + 120, x^29 + 106*x^27 + 116*x^26 + 123*x^25 + 4*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 28*x^18 + 123*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 9*x^9 + 28*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 4*x^2 + x + 116, x^29 + 106*x^27 + 16*x^26 + 99*x^25 + 96*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 48*x^18 + 83*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 33*x^9 + 32*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 80*x^2 + 41*x + 96, x^29 + 106*x^27 + 28*x^26 + 59*x^25 + 44*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 20*x^18 + 59*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 73*x^9 + 52*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 76*x^2 + 65*x + 124, x^29 + 106*x^27 + 76*x^26 + 107*x^25 + 12*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 36*x^18 + 11*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 25*x^9 + 84*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 60*x^2 + 113*x + 92, x^29 + 106*x^27 + 48*x^26 + 51*x^25 + 48*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 16*x^18 + 3*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 81*x^9 + 80*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 112*x^2 + 121*x + 112, x^29 + 106*x^27 + 92*x^26 + 123*x^25 + 44*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 20*x^18 + 59*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 9*x^9 + 52*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 76*x^2 + 65*x + 60, x^29 + 106*x^27 + 52*x^26 + 107*x^25 + 20*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 92*x^18 + 11*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 25*x^9 + 12*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 68*x^2 + 113*x + 68, x^29 + 106*x^27 + 84*x^26 + 59*x^25 + 100*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 60*x^18 + 59*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 73*x^9 + 60*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 100*x^2 + 65*x + 84, x^29 + 106*x^27 + 96*x^26 + 99*x^25 + 112*x^24 + 100*x^23 + 89*x^21 + 96*x^20 + 22*x^19 + 96*x^18 + 19*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 33*x^9 + 16*x^8 + 100*x^7 + 75*x^5 + 96*x^4 + 74*x^3 + 32*x^2 + 105*x + 112, x^29 + 106*x^27 + 100*x^26 + 27*x^25 + 20*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 108*x^18 + 91*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 105*x^9 + 12*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 52*x^2 + 33*x + 68, x^29 + 106*x^27 + 52*x^26 + 75*x^25 + 20*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 28*x^18 + 107*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 57*x^9 + 12*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 4*x^2 + 17*x + 4, x^29 + 106*x^27 + 72*x^26 + 83*x^25 + 72*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 88*x^18 + 35*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 49*x^9 + 120*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 104*x^2 + 89*x + 40, x^29 + 106*x^27 + 92*x^26 + 11*x^25 + 28*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 84*x^18 + 107*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 121*x^9 + 68*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 12*x^2 + 17*x + 44, x^29 + 106*x^27 + 16*x^26 + 3*x^25 + 96*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 22*x^19 + 112*x^18 + 115*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + x^9 + 32*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 74*x^3 + 16*x^2 + 9*x + 32, x^29 + 106*x^27 + 20*x^26 + 59*x^25 + 4*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 60*x^18 + 123*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 73*x^9 + 28*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 100*x^2 + x + 52, x^29 + 106*x^27 + 108*x^26 + 43*x^25 + 12*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 68*x^18 + 11*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 89*x^9 + 84*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 28*x^2 + 113*x + 28, x^29 + 106*x^27 + 44*x^26 + 59*x^25 + 92*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 4*x^18 + 123*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 73*x^9 + 4*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 92*x^2 + x + 44, x^29 + 106*x^27 + 100*x^26 + 75*x^25 + 100*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 108*x^18 + 43*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 57*x^9 + 60*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 52*x^2 + 81*x + 84, x^29 + 106*x^27 + 60*x^26 + 75*x^25 + 92*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 116*x^18 + 43*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 57*x^9 + 4*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 108*x^2 + 81*x + 108, x^29 + 106*x^27 + 48*x^26 + 67*x^25 + 100*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 80*x^18 + 51*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 65*x^9 + 100*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 48*x^2 + 73*x + 64, x^29 + 106*x^27 + 24*x^26 + 67*x^25 + 8*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 72*x^18 + 51*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 65*x^9 + 56*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 120*x^2 + 73*x + 104, x^29 + 106*x^27 + 20*x^26 + 107*x^25 + 116*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 124*x^18 + 11*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 25*x^9 + 44*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 36*x^2 + 113*x + 36, x^29 + 106*x^27 + 72*x^26 + 19*x^25 + 8*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 24*x^18 + 35*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 113*x^9 + 56*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 40*x^2 + 89*x + 40, x^29 + 106*x^27 + 112*x^26 + 3*x^25 + 36*x^23 + 32*x^22 + 89*x^21 + 86*x^19 + 80*x^18 + 51*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + x^9 + 36*x^7 + 32*x^6 + 75*x^5 + 10*x^3 + 48*x^2 + 73*x, x^29 + 106*x^27 + 20*x^26 + 43*x^25 + 20*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 124*x^18 + 75*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 89*x^9 + 12*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 36*x^2 + 49*x + 68, x^29 + 106*x^27 + 28*x^26 + 59*x^25 + 76*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 84*x^18 + 123*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 73*x^9 + 20*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 12*x^2 + x + 92, x^29 + 106*x^27 + 60*x^26 + 123*x^25 + 44*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 52*x^18 + 59*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 9*x^9 + 52*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 44*x^2 + 65*x + 60, x^29 + 106*x^27 + 4*x^26 + 43*x^25 + 68*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 12*x^18 + 11*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 89*x^9 + 92*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 20*x^2 + 113*x + 116, x^29 + 106*x^27 + 28*x^26 + 59*x^25 + 108*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 20*x^18 + 59*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 73*x^9 + 116*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 76*x^2 + 65*x + 60, x^29 + 106*x^27 + 68*x^26 + 43*x^25 + 4*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 76*x^18 + 11*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 89*x^9 + 28*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 84*x^2 + 113*x + 52, x^29 + 106*x^27 + 16*x^26 + 19*x^25 + 80*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 48*x^18 + 35*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 113*x^9 + 48*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 80*x^2 + 89*x + 16, x^29 + 106*x^27 + 56*x^26 + 67*x^25 + 72*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 104*x^18 + 115*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 65*x^9 + 120*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 88*x^2 + 9*x + 104, x^29 + 106*x^27 + 104*x^26 + 67*x^25 + 56*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 56*x^18 + 51*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 65*x^9 + 8*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 8*x^2 + 73*x + 88, x^29 + 106*x^27 + 80*x^26 + 35*x^25 + 32*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 112*x^18 + 19*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 97*x^9 + 96*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 16*x^2 + 105*x + 32, x^29 + 106*x^27 + 112*x^26 + 115*x^25 + 80*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 80*x^18 + 67*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 17*x^9 + 48*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 48*x^2 + 57*x + 16, x^29 + 106*x^27 + 120*x^26 + 115*x^25 + 120*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 40*x^18 + 67*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 17*x^9 + 72*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 24*x^2 + 57*x + 88, x^29 + 106*x^27 + 76*x^26 + 107*x^25 + 108*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 100*x^18 + 75*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 25*x^9 + 116*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 124*x^2 + 49*x + 124, x^29 + 106*x^27 + 8*x^26 + 115*x^25 + 8*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 24*x^18 + 3*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 17*x^9 + 56*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 40*x^2 + 121*x + 104, x^29 + 106*x^27 + 116*x^26 + 11*x^25 + 20*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 92*x^18 + 43*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 121*x^9 + 12*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 68*x^2 + 81*x + 4, x^29 + 106*x^27 + 88*x^26 + 19*x^25 + 56*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 72*x^18 + 35*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 113*x^9 + 8*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 120*x^2 + 89*x + 24, x^29 + 106*x^27 + 100*x^26 + 11*x^25 + 68*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 44*x^18 + 43*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 121*x^9 + 92*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 116*x^2 + 81*x + 116, x^29 + 106*x^27 + 96*x^26 + 67*x^25 + 48*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 86*x^19 + 32*x^18 + 115*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 65*x^9 + 80*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 10*x^3 + 96*x^2 + 9*x + 112, x^29 + 106*x^27 + 124*x^26 + 11*x^25 + 124*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 116*x^18 + 43*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 121*x^9 + 100*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 108*x^2 + 81*x + 76, x^29 + 106*x^27 + 4*x^26 + 123*x^25 + 20*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 12*x^18 + 59*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 9*x^9 + 12*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 20*x^2 + 65*x + 4, x^29 + 106*x^27 + 64*x^26 + 19*x^25 + 32*x^24 + 100*x^23 + 121*x^21 + 64*x^20 + 22*x^19 + 64*x^18 + 35*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 113*x^9 + 96*x^8 + 100*x^7 + 107*x^5 + 64*x^4 + 74*x^3 + 64*x^2 + 89*x + 32, x^29 + 106*x^27 + 104*x^26 + 19*x^25 + 72*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 120*x^18 + 35*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 113*x^9 + 120*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 72*x^2 + 89*x + 104, x^29 + 106*x^27 + 8*x^26 + 83*x^25 + 104*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 88*x^18 + 99*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 49*x^9 + 88*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 104*x^2 + 25*x + 8, x^29 + 106*x^27 + 12*x^26 + 27*x^25 + 124*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 100*x^18 + 91*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 105*x^9 + 100*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 124*x^2 + 33*x + 12, x^29 + 106*x^27 + 16*x^26 + 35*x^25 + 64*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 86*x^19 + 48*x^18 + 19*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 97*x^9 + 64*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 10*x^3 + 80*x^2 + 105*x + 64, x^29 + 106*x^27 + 35*x^25 + 16*x^24 + 36*x^23 + 25*x^21 + 96*x^20 + 86*x^19 + 19*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 97*x^9 + 112*x^8 + 36*x^7 + 11*x^5 + 96*x^4 + 10*x^3 + 105*x + 80, x^29 + 106*x^27 + 12*x^26 + 43*x^25 + 76*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 36*x^18 + 11*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 89*x^9 + 20*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 60*x^2 + 113*x + 92, x^29 + 106*x^27 + 16*x^26 + 3*x^25 + 96*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 48*x^18 + 51*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + x^9 + 32*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 80*x^2 + 73*x + 96, x^29 + 106*x^27 + 51*x^25 + 64*x^24 + 100*x^23 + 57*x^21 + 22*x^19 + 3*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 81*x^9 + 64*x^8 + 100*x^7 + 43*x^5 + 74*x^3 + 121*x + 64, x^29 + 106*x^27 + 16*x^26 + 35*x^25 + 32*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 48*x^18 + 19*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 97*x^9 + 96*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 80*x^2 + 105*x + 32, x^29 + 106*x^27 + 44*x^26 + 107*x^25 + 12*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 4*x^18 + 75*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 25*x^9 + 84*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 92*x^2 + 49*x + 28, x^29 + 106*x^27 + 68*x^26 + 107*x^25 + 36*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 12*x^18 + 11*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 25*x^9 + 124*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 20*x^2 + 113*x + 20, x^29 + 106*x^27 + 56*x^26 + 19*x^25 + 56*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 40*x^18 + 99*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 113*x^9 + 8*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 24*x^2 + 25*x + 88, x^29 + 106*x^27 + 52*x^26 + 11*x^25 + 116*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 92*x^18 + 107*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 121*x^9 + 44*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 68*x^2 + 17*x + 36, x^29 + 106*x^27 + 104*x^26 + 19*x^25 + 104*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 56*x^18 + 99*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 113*x^9 + 88*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 8*x^2 + 25*x + 72, x^29 + 106*x^27 + 28*x^26 + 107*x^25 + 28*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 84*x^18 + 75*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 25*x^9 + 68*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 12*x^2 + 49*x + 108, x^29 + 106*x^27 + 104*x^26 + 35*x^25 + 24*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 56*x^18 + 83*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 97*x^9 + 40*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 8*x^2 + 41*x + 56, x^29 + 106*x^27 + 36*x^26 + 43*x^25 + 4*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 108*x^18 + 11*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 89*x^9 + 28*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 52*x^2 + 113*x + 52, x^29 + 106*x^27 + 116*x^26 + 27*x^25 + 100*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 92*x^18 + 27*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 105*x^9 + 60*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 68*x^2 + 97*x + 20, x^29 + 106*x^27 + 12*x^26 + 11*x^25 + 108*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 100*x^18 + 107*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 121*x^9 + 116*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 124*x^2 + 17*x + 60, x^29 + 106*x^27 + 100*x^26 + 91*x^25 + 84*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 44*x^18 + 91*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 41*x^9 + 76*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 116*x^2 + 33*x + 68, x^29 + 106*x^27 + 116*x^26 + 91*x^25 + 100*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 28*x^18 + 27*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 41*x^9 + 60*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 4*x^2 + 97*x + 84, x^29 + 106*x^27 + 72*x^26 + 35*x^25 + 88*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 24*x^18 + 19*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 97*x^9 + 104*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 40*x^2 + 105*x + 56, x^29 + 106*x^27 + 120*x^26 + 3*x^25 + 72*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 40*x^18 + 51*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + x^9 + 120*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 24*x^2 + 73*x + 104, x^29 + 106*x^27 + 100*x^26 + 107*x^25 + 100*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 44*x^18 + 75*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 25*x^9 + 60*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 116*x^2 + 49*x + 20, x^29 + 106*x^27 + 4*x^26 + 43*x^25 + 36*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 12*x^18 + 11*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 89*x^9 + 124*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 20*x^2 + 113*x + 84, x^29 + 106*x^27 + 32*x^26 + 67*x^25 + 112*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 86*x^19 + 96*x^18 + 115*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 65*x^9 + 16*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 10*x^3 + 32*x^2 + 9*x + 48, x^29 + 106*x^27 + 116*x^26 + 75*x^25 + 116*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 92*x^18 + 107*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 57*x^9 + 44*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 68*x^2 + 17*x + 100, x^29 + 106*x^27 + 64*x^26 + 115*x^25 + 32*x^24 + 100*x^23 + 57*x^21 + 64*x^20 + 22*x^19 + 64*x^18 + 67*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 17*x^9 + 96*x^8 + 100*x^7 + 43*x^5 + 64*x^4 + 74*x^3 + 64*x^2 + 57*x + 32, x^29 + 106*x^27 + 112*x^26 + 51*x^25 + 48*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 16*x^18 + 67*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 81*x^9 + 80*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 112*x^2 + 57*x + 48, x^29 + 106*x^27 + 92*x^26 + 75*x^25 + 60*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 84*x^18 + 43*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 57*x^9 + 36*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 12*x^2 + 81*x + 76, x^29 + 106*x^27 + 8*x^26 + 115*x^25 + 104*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 88*x^18 + 67*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 17*x^9 + 88*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 104*x^2 + 57*x + 8, x^29 + 106*x^27 + 112*x^26 + 67*x^25 + 36*x^23 + 32*x^22 + 89*x^21 + 86*x^19 + 80*x^18 + 115*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 65*x^9 + 36*x^7 + 32*x^6 + 75*x^5 + 10*x^3 + 48*x^2 + 9*x, x^29 + 106*x^27 + 112*x^26 + 99*x^25 + 96*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 22*x^19 + 16*x^18 + 19*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 33*x^9 + 32*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 74*x^3 + 112*x^2 + 105*x + 32, x^29 + 106*x^27 + 35*x^25 + 80*x^24 + 36*x^23 + 25*x^21 + 96*x^20 + 86*x^19 + 19*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 97*x^9 + 48*x^8 + 36*x^7 + 11*x^5 + 96*x^4 + 10*x^3 + 105*x + 16, x^29 + 106*x^27 + 108*x^26 + 43*x^25 + 76*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 68*x^18 + 11*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 89*x^9 + 20*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 28*x^2 + 113*x + 92, x^29 + 106*x^27 + 20*x^26 + 107*x^25 + 52*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 124*x^18 + 11*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 25*x^9 + 108*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 36*x^2 + 113*x + 100, x^29 + 106*x^27 + 28*x^26 + 91*x^25 + 108*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 84*x^18 + 91*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 41*x^9 + 116*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 12*x^2 + 33*x + 124, x^29 + 106*x^27 + 24*x^26 + 19*x^25 + 24*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 72*x^18 + 99*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 113*x^9 + 40*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 120*x^2 + 25*x + 56, x^29 + 106*x^27 + 24*x^26 + 83*x^25 + 24*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 72*x^18 + 35*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 49*x^9 + 40*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 120*x^2 + 89*x + 56, x^29 + 106*x^27 + 92*x^26 + 91*x^25 + 76*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 20*x^18 + 91*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 41*x^9 + 20*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 76*x^2 + 33*x + 92, x^29 + 106*x^27 + 96*x^26 + 115*x^25 + 96*x^24 + 36*x^23 + 121*x^21 + 86*x^19 + 96*x^18 + 3*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 17*x^9 + 32*x^8 + 36*x^7 + 107*x^5 + 10*x^3 + 32*x^2 + 121*x + 32, x^29 + 106*x^27 + 12*x^26 + 27*x^25 + 28*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 36*x^18 + 27*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 105*x^9 + 68*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 60*x^2 + 97*x + 108, x^29 + 106*x^27 + 36*x^26 + 11*x^25 + 68*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 44*x^18 + 107*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 121*x^9 + 92*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 116*x^2 + 17*x + 52, x^29 + 106*x^27 + 124*x^26 + 11*x^25 + 60*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 116*x^18 + 43*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 121*x^9 + 36*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 108*x^2 + 81*x + 12, x^29 + 106*x^27 + 12*x^26 + 107*x^25 + 12*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 100*x^18 + 11*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 25*x^9 + 84*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 124*x^2 + 113*x + 92, x^29 + 106*x^27 + 60*x^26 + 91*x^25 + 44*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 116*x^18 + 27*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 41*x^9 + 52*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 108*x^2 + 97*x + 124, x^29 + 106*x^27 + 96*x^26 + 19*x^25 + 64*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 22*x^19 + 32*x^18 + 35*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 113*x^9 + 64*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 74*x^3 + 96*x^2 + 89*x + 64, x^29 + 106*x^27 + 80*x^26 + 99*x^25 + 32*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 22*x^19 + 48*x^18 + 19*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 33*x^9 + 96*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 74*x^3 + 80*x^2 + 105*x + 96, x^29 + 106*x^27 + 84*x^26 + 43*x^25 + 116*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 124*x^18 + 11*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 89*x^9 + 44*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 36*x^2 + 113*x + 100, x^29 + 106*x^27 + 4*x^26 + 59*x^25 + 20*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 76*x^18 + 59*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 73*x^9 + 12*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 84*x^2 + 65*x + 68, x^29 + 106*x^27 + 104*x^26 + 115*x^25 + 8*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 56*x^18 + 3*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 17*x^9 + 56*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 8*x^2 + 121*x + 104, x^29 + 106*x^27 + 36*x^26 + 11*x^25 + 68*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 108*x^18 + 43*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 121*x^9 + 92*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 52*x^2 + 81*x + 116, x^29 + 106*x^27 + 52*x^26 + 123*x^25 + 100*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 92*x^18 + 123*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 9*x^9 + 60*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 68*x^2 + x + 84, x^29 + 106*x^27 + 124*x^26 + 43*x^25 + 60*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 116*x^18 + 11*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 89*x^9 + 36*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 108*x^2 + 113*x + 12, x^29 + 106*x^27 + 56*x^26 + 83*x^25 + 88*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 40*x^18 + 35*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 49*x^9 + 104*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 24*x^2 + 89*x + 120, x^29 + 106*x^27 + 40*x^26 + 51*x^25 + 40*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 120*x^18 + 67*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 81*x^9 + 24*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 72*x^2 + 57*x + 8, x^29 + 106*x^27 + 24*x^26 + 99*x^25 + 8*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 8*x^18 + 83*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 33*x^9 + 56*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 56*x^2 + 41*x + 40, x^29 + 106*x^27 + 36*x^26 + 107*x^25 + 100*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 44*x^18 + 11*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 25*x^9 + 60*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 116*x^2 + 113*x + 84, x^29 + 106*x^27 + 32*x^26 + 99*x^25 + 112*x^24 + 100*x^23 + 89*x^21 + 96*x^20 + 22*x^19 + 32*x^18 + 19*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 33*x^9 + 16*x^8 + 100*x^7 + 75*x^5 + 96*x^4 + 74*x^3 + 96*x^2 + 105*x + 112, x^29 + 106*x^27 + 116*x^26 + 43*x^25 + 84*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 28*x^18 + 75*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 89*x^9 + 76*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 4*x^2 + 49*x + 4, x^29 + 106*x^27 + 68*x^26 + 43*x^25 + 100*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 12*x^18 + 75*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 89*x^9 + 60*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 20*x^2 + 49*x + 84, x^29 + 106*x^27 + 64*x^26 + 67*x^25 + 16*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 22*x^19 + 51*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 65*x^9 + 112*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 74*x^3 + 73*x + 16, x^29 + 106*x^27 + 64*x^26 + 99*x^25 + 112*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 22*x^19 + 19*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 33*x^9 + 16*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 74*x^3 + 105*x + 112, x^29 + 106*x^27 + 44*x^26 + 59*x^25 + 124*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 4*x^18 + 123*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 73*x^9 + 100*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 92*x^2 + x + 76, x^29 + 106*x^27 + 76*x^26 + 27*x^25 + 124*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 36*x^18 + 91*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 105*x^9 + 100*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 60*x^2 + 33*x + 12, x^29 + 106*x^27 + 44*x^26 + 27*x^25 + 124*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 4*x^18 + 27*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 105*x^9 + 100*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 92*x^2 + 97*x + 76, x^29 + 106*x^27 + 108*x^26 + 75*x^25 + 12*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 68*x^18 + 107*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 57*x^9 + 84*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 28*x^2 + 17*x + 28, x^29 + 106*x^27 + 72*x^26 + 99*x^25 + 88*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 24*x^18 + 83*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 33*x^9 + 104*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 40*x^2 + 41*x + 56, x^29 + 106*x^27 + 84*x^26 + 91*x^25 + 100*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 60*x^18 + 27*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 41*x^9 + 60*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 100*x^2 + 97*x + 84, x^29 + 106*x^27 + 44*x^26 + 75*x^25 + 76*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 4*x^18 + 107*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 57*x^9 + 20*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 92*x^2 + 17*x + 92, x^29 + 106*x^27 + 99*x^25 + 112*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 22*x^19 + 64*x^18 + 19*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 33*x^9 + 16*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 74*x^3 + 64*x^2 + 105*x + 112, x^29 + 106*x^27 + 80*x^26 + 35*x^25 + 64*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 86*x^19 + 112*x^18 + 19*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 97*x^9 + 64*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 10*x^3 + 16*x^2 + 105*x + 64, x^29 + 106*x^27 + 44*x^26 + 11*x^25 + 108*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 4*x^18 + 43*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 121*x^9 + 116*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 92*x^2 + 81*x + 124, x^29 + 106*x^27 + 52*x^26 + 75*x^25 + 116*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 92*x^18 + 43*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 57*x^9 + 44*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 68*x^2 + 81*x + 36, x^29 + 106*x^27 + 100*x^26 + 91*x^25 + 20*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 44*x^18 + 91*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 41*x^9 + 12*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 116*x^2 + 33*x + 4, x^29 + 106*x^27 + 52*x^26 + 107*x^25 + 52*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 92*x^18 + 11*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 25*x^9 + 108*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 68*x^2 + 113*x + 100, x^29 + 106*x^27 + 4*x^26 + 75*x^25 + 100*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 12*x^18 + 107*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 57*x^9 + 60*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 20*x^2 + 17*x + 20, x^29 + 106*x^27 + 64*x^26 + 83*x^25 + 64*x^24 + 100*x^23 + 121*x^21 + 22*x^19 + 64*x^18 + 99*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 49*x^9 + 64*x^8 + 100*x^7 + 107*x^5 + 74*x^3 + 64*x^2 + 25*x + 64, x^29 + 106*x^27 + 60*x^26 + 27*x^25 + 108*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 116*x^18 + 91*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 105*x^9 + 116*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 108*x^2 + 33*x + 60, x^29 + 106*x^27 + 52*x^26 + 11*x^25 + 116*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 28*x^18 + 43*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 121*x^9 + 44*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 4*x^2 + 81*x + 100, x^29 + 106*x^27 + 36*x^26 + 59*x^25 + 84*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 44*x^18 + 59*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 73*x^9 + 76*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 116*x^2 + 65*x + 4, x^29 + 106*x^27 + 72*x^26 + 115*x^25 + 8*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 88*x^18 + 3*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 17*x^9 + 56*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 104*x^2 + 121*x + 104, x^29 + 106*x^27 + 32*x^26 + 35*x^25 + 112*x^24 + 100*x^23 + 89*x^21 + 96*x^20 + 22*x^19 + 32*x^18 + 83*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 97*x^9 + 16*x^8 + 100*x^7 + 75*x^5 + 96*x^4 + 74*x^3 + 96*x^2 + 41*x + 112, x^29 + 106*x^27 + 28*x^26 + 27*x^25 + 44*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 20*x^18 + 91*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 105*x^9 + 52*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 76*x^2 + 33*x + 124, x^29 + 106*x^27 + 64*x^26 + 19*x^25 + 64*x^24 + 100*x^23 + 121*x^21 + 22*x^19 + 64*x^18 + 35*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 113*x^9 + 64*x^8 + 100*x^7 + 107*x^5 + 74*x^3 + 64*x^2 + 89*x + 64, x^29 + 106*x^27 + 44*x^26 + 107*x^25 + 108*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 4*x^18 + 75*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 25*x^9 + 116*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 92*x^2 + 49*x + 124, x^29 + 106*x^27 + 20*x^26 + 11*x^25 + 84*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 60*x^18 + 43*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 121*x^9 + 76*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 100*x^2 + 81*x + 68, x^29 + 106*x^27 + 84*x^26 + 11*x^25 + 20*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 60*x^18 + 107*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 121*x^9 + 12*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 100*x^2 + 17*x + 68, x^29 + 106*x^27 + 56*x^26 + 99*x^25 + 40*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 104*x^18 + 83*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 33*x^9 + 24*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 88*x^2 + 41*x + 72, x^29 + 106*x^27 + 56*x^26 + 67*x^25 + 40*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 104*x^18 + 115*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 65*x^9 + 24*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 88*x^2 + 9*x + 72, x^29 + 106*x^27 + 32*x^26 + 35*x^25 + 16*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 86*x^19 + 96*x^18 + 19*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 97*x^9 + 112*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 10*x^3 + 32*x^2 + 105*x + 80, x^29 + 106*x^27 + 60*x^26 + 75*x^25 + 124*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 52*x^18 + 107*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 57*x^9 + 100*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 44*x^2 + 17*x + 76, x^29 + 106*x^27 + 112*x^26 + 19*x^25 + 112*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 80*x^18 + 35*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 113*x^9 + 16*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 48*x^2 + 89*x + 48, x^29 + 106*x^27 + 108*x^26 + 11*x^25 + 12*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 68*x^18 + 43*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 121*x^9 + 84*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 28*x^2 + 81*x + 28, x^29 + 106*x^27 + 60*x^26 + 123*x^25 + 12*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 52*x^18 + 59*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 9*x^9 + 84*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 44*x^2 + 65*x + 28, x^29 + 106*x^27 + 52*x^26 + 59*x^25 + 36*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 92*x^18 + 59*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 73*x^9 + 124*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 68*x^2 + 65*x + 20, x^29 + 106*x^27 + 32*x^26 + 99*x^25 + 48*x^24 + 100*x^23 + 89*x^21 + 96*x^20 + 22*x^19 + 32*x^18 + 19*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 33*x^9 + 80*x^8 + 100*x^7 + 75*x^5 + 96*x^4 + 74*x^3 + 96*x^2 + 105*x + 48, x^29 + 106*x^27 + 36*x^26 + 59*x^25 + 52*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 44*x^18 + 59*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 73*x^9 + 108*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 116*x^2 + 65*x + 100, x^29 + 106*x^27 + 24*x^26 + 67*x^25 + 72*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 72*x^18 + 51*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 65*x^9 + 120*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 120*x^2 + 73*x + 40, x^29 + 106*x^27 + 92*x^26 + 75*x^25 + 92*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 20*x^18 + 107*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 57*x^9 + 4*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 76*x^2 + 17*x + 44, x^29 + 106*x^27 + 108*x^26 + 91*x^25 + 60*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 68*x^18 + 91*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 41*x^9 + 36*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 28*x^2 + 33*x + 12, x^29 + 106*x^27 + 108*x^26 + 107*x^25 + 12*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 4*x^18 + 11*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 25*x^9 + 84*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 92*x^2 + 113*x + 92, x^29 + 106*x^27 + 19*x^25 + 100*x^23 + 121*x^21 + 22*x^19 + 35*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 113*x^9 + 100*x^7 + 107*x^5 + 74*x^3 + 89*x, x^29 + 106*x^27 + 99*x^25 + 48*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 22*x^19 + 64*x^18 + 19*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 33*x^9 + 80*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 74*x^3 + 64*x^2 + 105*x + 48, x^29 + 106*x^27 + 40*x^26 + 99*x^25 + 120*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 56*x^18 + 83*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 33*x^9 + 72*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 8*x^2 + 41*x + 88, x^29 + 106*x^27 + 4*x^26 + 11*x^25 + 100*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 12*x^18 + 43*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 121*x^9 + 60*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 20*x^2 + 81*x + 20, x^29 + 106*x^27 + 20*x^26 + 75*x^25 + 84*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 60*x^18 + 107*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 57*x^9 + 76*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 100*x^2 + 17*x + 68, x^29 + 106*x^27 + 32*x^26 + 51*x^25 + 64*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 22*x^19 + 96*x^18 + 3*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 81*x^9 + 64*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 74*x^3 + 32*x^2 + 121*x + 64, x^29 + 106*x^27 + 124*x^26 + 107*x^25 + 92*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 116*x^18 + 75*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 25*x^9 + 4*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 108*x^2 + 49*x + 44, x^29 + 106*x^27 + 28*x^26 + 91*x^25 + 108*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 20*x^18 + 27*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 41*x^9 + 116*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 76*x^2 + 97*x + 60, x^29 + 106*x^27 + 52*x^26 + 123*x^25 + 36*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 28*x^18 + 59*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 9*x^9 + 124*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 4*x^2 + 65*x + 84, x^29 + 106*x^27 + 36*x^26 + 11*x^25 + 4*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 108*x^18 + 43*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 121*x^9 + 28*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 52*x^2 + 81*x + 52, x^29 + 106*x^27 + 52*x^26 + 91*x^25 + 68*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 92*x^18 + 27*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 41*x^9 + 92*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 68*x^2 + 97*x + 52, x^29 + 106*x^27 + 24*x^26 + 19*x^25 + 120*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 8*x^18 + 35*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 113*x^9 + 72*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 56*x^2 + 89*x + 88, x^29 + 106*x^27 + 48*x^26 + 51*x^25 + 16*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 80*x^18 + 67*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 81*x^9 + 112*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 48*x^2 + 57*x + 16, x^29 + 106*x^27 + 64*x^26 + 115*x^25 + 64*x^24 + 100*x^23 + 57*x^21 + 22*x^19 + 64*x^18 + 67*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 17*x^9 + 64*x^8 + 100*x^7 + 43*x^5 + 74*x^3 + 64*x^2 + 57*x + 64, x^29 + 106*x^27 + 12*x^26 + 107*x^25 + 108*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 36*x^18 + 75*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 25*x^9 + 116*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 60*x^2 + 49*x + 124, x^29 + 106*x^27 + 40*x^26 + 3*x^25 + 56*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 56*x^18 + 51*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + x^9 + 8*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 8*x^2 + 73*x + 24, x^29 + 106*x^27 + 88*x^26 + 19*x^25 + 24*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 8*x^18 + 99*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 113*x^9 + 40*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 56*x^2 + 25*x + 56, x^29 + 106*x^27 + 52*x^26 + 27*x^25 + 100*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 28*x^18 + 27*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 105*x^9 + 60*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 4*x^2 + 97*x + 20, x^29 + 106*x^27 + 76*x^26 + 43*x^25 + 76*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 100*x^18 + 11*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 89*x^9 + 20*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 124*x^2 + 113*x + 92, x^29 + 106*x^27 + 24*x^26 + 19*x^25 + 88*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 8*x^18 + 35*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 113*x^9 + 104*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 56*x^2 + 89*x + 56, x^29 + 106*x^27 + 88*x^26 + 35*x^25 + 72*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 8*x^18 + 83*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 97*x^9 + 120*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 56*x^2 + 41*x + 40, x^29 + 106*x^27 + 112*x^26 + 51*x^25 + 112*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 80*x^18 + 3*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 81*x^9 + 16*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 48*x^2 + 121*x + 48, x^29 + 106*x^27 + 28*x^26 + 107*x^25 + 60*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 20*x^18 + 11*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 25*x^9 + 36*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 76*x^2 + 113*x + 76, x^29 + 106*x^27 + 60*x^26 + 11*x^25 + 124*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 116*x^18 + 107*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 121*x^9 + 100*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 108*x^2 + 17*x + 12, x^29 + 106*x^27 + 8*x^26 + 19*x^25 + 40*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 24*x^18 + 99*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 113*x^9 + 24*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 40*x^2 + 25*x + 8, x^29 + 106*x^27 + 80*x^26 + 83*x^25 + 112*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 48*x^18 + 35*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 49*x^9 + 16*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 80*x^2 + 89*x + 112, x^29 + 106*x^27 + 36*x^26 + 123*x^25 + 116*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 44*x^18 + 123*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 9*x^9 + 44*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 116*x^2 + x + 36, x^29 + 106*x^27 + 108*x^26 + 123*x^25 + 124*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 4*x^18 + 123*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 9*x^9 + 100*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 92*x^2 + x + 12, x^29 + 106*x^27 + 112*x^26 + 67*x^25 + 64*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 86*x^19 + 80*x^18 + 115*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 65*x^9 + 64*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 10*x^3 + 48*x^2 + 9*x + 64, x^29 + 106*x^27 + 108*x^26 + 75*x^25 + 76*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 68*x^18 + 107*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 57*x^9 + 20*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 28*x^2 + 17*x + 92, x^29 + 106*x^27 + 4*x^26 + 123*x^25 + 20*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 76*x^18 + 123*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 9*x^9 + 12*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 84*x^2 + x + 68, x^29 + 106*x^27 + 104*x^26 + 99*x^25 + 88*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 120*x^18 + 83*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 33*x^9 + 104*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 72*x^2 + 41*x + 56, x^29 + 106*x^27 + 8*x^26 + 115*x^25 + 40*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 24*x^18 + 3*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 17*x^9 + 24*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 40*x^2 + 121*x + 8, x^29 + 106*x^27 + 8*x^26 + 35*x^25 + 56*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 88*x^18 + 19*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 97*x^9 + 8*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 104*x^2 + 105*x + 24, x^29 + 106*x^27 + 20*x^26 + 123*x^25 + 100*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 60*x^18 + 59*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 9*x^9 + 60*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 100*x^2 + 65*x + 20, x^29 + 106*x^27 + 52*x^26 + 43*x^25 + 116*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 28*x^18 + 11*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 89*x^9 + 44*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 4*x^2 + 113*x + 100, x^29 + 106*x^27 + 96*x^26 + 51*x^25 + 36*x^23 + 121*x^21 + 64*x^20 + 86*x^19 + 96*x^18 + 67*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 81*x^9 + 36*x^7 + 107*x^5 + 64*x^4 + 10*x^3 + 32*x^2 + 57*x + 64, x^29 + 106*x^27 + 56*x^26 + 51*x^25 + 88*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 104*x^18 + 3*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 81*x^9 + 104*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 88*x^2 + 121*x + 56, x^29 + 106*x^27 + 84*x^26 + 27*x^25 + 4*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 124*x^18 + 27*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 105*x^9 + 28*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 36*x^2 + 97*x + 52, x^29 + 106*x^27 + 68*x^26 + 91*x^25 + 52*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 76*x^18 + 91*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 41*x^9 + 108*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 84*x^2 + 33*x + 36, x^29 + 106*x^27 + 20*x^26 + 11*x^25 + 52*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 124*x^18 + 107*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 121*x^9 + 108*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 36*x^2 + 17*x + 100, x^29 + 106*x^27 + 76*x^26 + 107*x^25 + 108*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 36*x^18 + 11*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 25*x^9 + 116*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 60*x^2 + 113*x + 60, x^29 + 106*x^27 + 36*x^26 + 123*x^25 + 116*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 108*x^18 + 59*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 9*x^9 + 44*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 52*x^2 + 65*x + 100, x^29 + 106*x^27 + 48*x^26 + 19*x^25 + 48*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 16*x^18 + 35*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 113*x^9 + 80*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 112*x^2 + 89*x + 112, x^29 + 106*x^27 + 16*x^26 + 83*x^25 + 112*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 112*x^18 + 35*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 49*x^9 + 16*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 16*x^2 + 89*x + 112, x^29 + 106*x^27 + 20*x^26 + 75*x^25 + 20*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 60*x^18 + 107*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 57*x^9 + 12*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 100*x^2 + 17*x + 4, x^29 + 106*x^27 + 16*x^26 + 67*x^25 + 32*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 22*x^19 + 112*x^18 + 51*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 65*x^9 + 96*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 74*x^3 + 16*x^2 + 73*x + 96, x^29 + 106*x^27 + 8*x^26 + 3*x^25 + 24*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 24*x^18 + 115*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + x^9 + 40*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 40*x^2 + 9*x + 56, x^29 + 106*x^27 + 16*x^26 + 83*x^25 + 112*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 48*x^18 + 99*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 49*x^9 + 16*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 80*x^2 + 25*x + 48, x^29 + 106*x^27 + 96*x^26 + 99*x^25 + 16*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 86*x^19 + 32*x^18 + 83*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 33*x^9 + 112*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 10*x^3 + 96*x^2 + 41*x + 80, x^29 + 106*x^27 + 20*x^26 + 75*x^25 + 52*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 60*x^18 + 107*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 57*x^9 + 108*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 100*x^2 + 17*x + 36, x^29 + 106*x^27 + 52*x^26 + 91*x^25 + 36*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 92*x^18 + 27*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 41*x^9 + 124*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 68*x^2 + 97*x + 20, x^29 + 106*x^27 + 124*x^26 + 75*x^25 + 60*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 116*x^18 + 107*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 57*x^9 + 36*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 108*x^2 + 17*x + 12, x^29 + 106*x^27 + 28*x^26 + 75*x^25 + 124*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 20*x^18 + 43*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 57*x^9 + 100*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 76*x^2 + 81*x + 12, x^29 + 106*x^27 + 100*x^26 + 43*x^25 + 100*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 108*x^18 + 75*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 89*x^9 + 60*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 52*x^2 + 49*x + 84, x^29 + 106*x^27 + 20*x^26 + 43*x^25 + 116*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 60*x^18 + 11*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 89*x^9 + 44*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 100*x^2 + 113*x + 100, x^29 + 106*x^27 + 120*x^26 + 83*x^25 + 120*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 40*x^18 + 99*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 49*x^9 + 72*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 24*x^2 + 25*x + 88, x^29 + 106*x^27 + 64*x^26 + 67*x^25 + 112*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 22*x^19 + 51*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 65*x^9 + 16*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 74*x^3 + 73*x + 112, x^29 + 106*x^27 + 44*x^26 + 27*x^25 + 92*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 4*x^18 + 27*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 105*x^9 + 4*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 92*x^2 + 97*x + 44, x^29 + 106*x^27 + 8*x^26 + 35*x^25 + 56*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 24*x^18 + 83*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 97*x^9 + 8*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 40*x^2 + 41*x + 88, x^29 + 106*x^27 + 108*x^26 + 107*x^25 + 12*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 68*x^18 + 75*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 25*x^9 + 84*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 28*x^2 + 49*x + 28, x^29 + 106*x^27 + 12*x^26 + 123*x^25 + 92*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 36*x^18 + 59*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 9*x^9 + 4*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 60*x^2 + 65*x + 44, x^29 + 106*x^27 + 67*x^25 + 112*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 22*x^19 + 64*x^18 + 51*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 65*x^9 + 16*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 74*x^3 + 64*x^2 + 73*x + 112, x^29 + 106*x^27 + 48*x^26 + 3*x^25 + 100*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 80*x^18 + 115*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + x^9 + 100*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 48*x^2 + 9*x + 64, x^29 + 106*x^27 + 64*x^26 + 99*x^25 + 48*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 22*x^19 + 19*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 33*x^9 + 80*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 74*x^3 + 105*x + 48, x^29 + 106*x^27 + 124*x^26 + 123*x^25 + 44*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 116*x^18 + 59*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 9*x^9 + 52*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 108*x^2 + 65*x + 60, x^29 + 106*x^27 + 124*x^26 + 123*x^25 + 12*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 52*x^18 + 123*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 9*x^9 + 84*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 44*x^2 + x + 92, x^29 + 106*x^27 + 88*x^26 + 99*x^25 + 8*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 8*x^18 + 19*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 33*x^9 + 56*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 56*x^2 + 105*x + 104, x^29 + 106*x^27 + 88*x^26 + 19*x^25 + 88*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 72*x^18 + 35*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 113*x^9 + 104*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 120*x^2 + 89*x + 56, x^29 + 106*x^27 + 88*x^26 + 99*x^25 + 72*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 8*x^18 + 19*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 33*x^9 + 120*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 56*x^2 + 105*x + 40, x^29 + 106*x^27 + 20*x^26 + 75*x^25 + 84*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 124*x^18 + 43*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 57*x^9 + 76*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 36*x^2 + 81*x + 4, x^29 + 106*x^27 + 120*x^26 + 67*x^25 + 8*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 40*x^18 + 115*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 65*x^9 + 56*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 24*x^2 + 9*x + 40, x^29 + 106*x^27 + 16*x^26 + 99*x^25 + 100*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 112*x^18 + 19*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 33*x^9 + 100*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 16*x^2 + 105*x + 64, x^29 + 106*x^27 + 28*x^26 + 11*x^25 + 124*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 20*x^18 + 107*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 121*x^9 + 100*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 76*x^2 + 17*x + 12, x^29 + 106*x^27 + 68*x^26 + 107*x^25 + 4*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 12*x^18 + 11*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 25*x^9 + 28*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 20*x^2 + 113*x + 116, x^29 + 106*x^27 + 19*x^25 + 96*x^24 + 100*x^23 + 121*x^21 + 64*x^20 + 22*x^19 + 35*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 113*x^9 + 32*x^8 + 100*x^7 + 107*x^5 + 64*x^4 + 74*x^3 + 89*x + 96, x^29 + 106*x^27 + 80*x^26 + 3*x^25 + 32*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 112*x^18 + 51*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + x^9 + 96*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 16*x^2 + 73*x + 32, x^29 + 106*x^27 + 124*x^26 + 59*x^25 + 76*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 116*x^18 + 123*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 73*x^9 + 20*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 108*x^2 + x + 92, x^29 + 106*x^27 + 108*x^26 + 107*x^25 + 44*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 4*x^18 + 11*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 25*x^9 + 52*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 92*x^2 + 113*x + 124, x^29 + 106*x^27 + 116*x^26 + 43*x^25 + 52*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 28*x^18 + 75*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 89*x^9 + 108*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 4*x^2 + 49*x + 100, x^29 + 106*x^27 + 40*x^26 + 51*x^25 + 40*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 56*x^18 + 3*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 81*x^9 + 24*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 8*x^2 + 121*x + 72, x^29 + 106*x^27 + 8*x^26 + 35*x^25 + 88*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 88*x^18 + 19*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 97*x^9 + 104*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 104*x^2 + 105*x + 56, x^29 + 106*x^27 + 116*x^26 + 107*x^25 + 20*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 92*x^18 + 75*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 25*x^9 + 12*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 68*x^2 + 49*x + 4, x^29 + 106*x^27 + 24*x^26 + 35*x^25 + 104*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 8*x^18 + 19*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 97*x^9 + 88*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 56*x^2 + 105*x + 8, x^29 + 106*x^27 + 20*x^26 + 27*x^25 + 4*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 124*x^18 + 91*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 105*x^9 + 28*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 36*x^2 + 33*x + 116, x^29 + 106*x^27 + 20*x^26 + 107*x^25 + 84*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 60*x^18 + 75*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 25*x^9 + 76*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 100*x^2 + 49*x + 68, x^29 + 106*x^27 + 67*x^25 + 16*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 22*x^19 + 64*x^18 + 51*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 65*x^9 + 112*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 74*x^3 + 64*x^2 + 73*x + 16, x^29 + 106*x^27 + 20*x^26 + 59*x^25 + 4*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 124*x^18 + 59*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 73*x^9 + 28*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 36*x^2 + 65*x + 116, x^29 + 106*x^27 + 52*x^26 + 91*x^25 + 100*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 92*x^18 + 27*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 41*x^9 + 60*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 68*x^2 + 97*x + 84, x^29 + 106*x^27 + 60*x^26 + 107*x^25 + 124*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 52*x^18 + 75*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 25*x^9 + 100*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 44*x^2 + 49*x + 76, x^29 + 106*x^27 + 84*x^26 + 107*x^25 + 20*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 60*x^18 + 11*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 25*x^9 + 12*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 100*x^2 + 113*x + 68, x^29 + 106*x^27 + 120*x^26 + 99*x^25 + 104*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 40*x^18 + 83*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 33*x^9 + 88*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 24*x^2 + 41*x + 8, x^29 + 106*x^27 + 36*x^26 + 59*x^25 + 116*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 108*x^18 + 123*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 73*x^9 + 44*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 52*x^2 + x + 100, x^29 + 106*x^27 + 120*x^26 + 35*x^25 + 40*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 40*x^18 + 19*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 97*x^9 + 24*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 24*x^2 + 105*x + 72, x^29 + 106*x^27 + 96*x^26 + 3*x^25 + 112*x^24 + 100*x^23 + 25*x^21 + 96*x^20 + 22*x^19 + 96*x^18 + 115*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + x^9 + 16*x^8 + 100*x^7 + 11*x^5 + 96*x^4 + 74*x^3 + 32*x^2 + 9*x + 112, x^29 + 106*x^27 + 84*x^26 + 59*x^25 + 36*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 60*x^18 + 59*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 73*x^9 + 124*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 100*x^2 + 65*x + 20, x^29 + 106*x^27 + 64*x^26 + 3*x^25 + 112*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 22*x^19 + 115*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + x^9 + 16*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 74*x^3 + 9*x + 112, x^29 + 106*x^27 + 92*x^26 + 43*x^25 + 124*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 84*x^18 + 75*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 89*x^9 + 100*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 12*x^2 + 49*x + 12, x^29 + 106*x^27 + 32*x^26 + 115*x^25 + 32*x^24 + 36*x^23 + 121*x^21 + 86*x^19 + 32*x^18 + 3*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 17*x^9 + 96*x^8 + 36*x^7 + 107*x^5 + 10*x^3 + 96*x^2 + 121*x + 96, x^29 + 106*x^27 + 3*x^25 + 16*x^24 + 36*x^23 + 89*x^21 + 96*x^20 + 86*x^19 + 51*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + x^9 + 112*x^8 + 36*x^7 + 75*x^5 + 96*x^4 + 10*x^3 + 73*x + 80, x^29 + 106*x^27 + 36*x^26 + 123*x^25 + 52*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 44*x^18 + 123*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 9*x^9 + 108*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 116*x^2 + x + 100, x^29 + 106*x^27 + 24*x^26 + 83*x^25 + 24*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 8*x^18 + 99*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 49*x^9 + 40*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 56*x^2 + 25*x + 120, x^29 + 106*x^27 + 64*x^26 + 115*x^25 + 32*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 86*x^19 + 3*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 17*x^9 + 96*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 10*x^3 + 121*x + 96, x^29 + 106*x^27 + 96*x^26 + 115*x^25 + 96*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 22*x^19 + 32*x^18 + 67*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 17*x^9 + 32*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 74*x^3 + 96*x^2 + 57*x + 96, x^29 + 106*x^27 + 67*x^25 + 48*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 22*x^19 + 64*x^18 + 51*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 65*x^9 + 80*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 74*x^3 + 64*x^2 + 73*x + 48, x^29 + 106*x^27 + 96*x^26 + 67*x^25 + 112*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 86*x^19 + 32*x^18 + 115*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 65*x^9 + 16*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 10*x^3 + 96*x^2 + 9*x + 48, x^29 + 106*x^27 + 80*x^26 + 35*x^25 + 96*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 112*x^18 + 19*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 97*x^9 + 32*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 16*x^2 + 105*x + 96, x^29 + 106*x^27 + 72*x^26 + 51*x^25 + 104*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 24*x^18 + 3*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 81*x^9 + 88*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 40*x^2 + 121*x + 8, x^29 + 106*x^27 + 115*x^25 + 32*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 86*x^19 + 64*x^18 + 3*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 17*x^9 + 96*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 10*x^3 + 64*x^2 + 121*x + 96, x^29 + 106*x^27 + 104*x^26 + 67*x^25 + 24*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 56*x^18 + 51*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 65*x^9 + 40*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 8*x^2 + 73*x + 56, x^29 + 106*x^27 + 40*x^26 + 3*x^25 + 120*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 56*x^18 + 51*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + x^9 + 72*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 8*x^2 + 73*x + 88, x^29 + 106*x^27 + 124*x^26 + 43*x^25 + 28*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 116*x^18 + 11*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 89*x^9 + 68*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 108*x^2 + 113*x + 108, x^29 + 106*x^27 + 60*x^26 + 43*x^25 + 92*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 52*x^18 + 11*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 89*x^9 + 4*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 44*x^2 + 113*x + 44, x^29 + 106*x^27 + 88*x^26 + 3*x^25 + 104*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 72*x^18 + 51*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + x^9 + 88*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 120*x^2 + 73*x + 8, x^29 + 106*x^27 + 56*x^26 + 19*x^25 + 120*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 40*x^18 + 99*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 113*x^9 + 72*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 24*x^2 + 25*x + 24, x^29 + 106*x^27 + 56*x^26 + 115*x^25 + 24*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 104*x^18 + 67*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 17*x^9 + 40*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 88*x^2 + 57*x + 120, x^29 + 106*x^27 + 36*x^26 + 107*x^25 + 4*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 108*x^18 + 75*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 25*x^9 + 28*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 52*x^2 + 49*x + 52, x^29 + 106*x^27 + 12*x^26 + 107*x^25 + 44*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 100*x^18 + 11*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 25*x^9 + 52*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 124*x^2 + 113*x + 124, x^29 + 106*x^27 + 115*x^25 + 96*x^24 + 100*x^23 + 57*x^21 + 64*x^20 + 22*x^19 + 67*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 17*x^9 + 32*x^8 + 100*x^7 + 43*x^5 + 64*x^4 + 74*x^3 + 57*x + 96, x^29 + 106*x^27 + 60*x^26 + 123*x^25 + 44*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 116*x^18 + 123*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 9*x^9 + 52*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 108*x^2 + x + 124, x^29 + 106*x^27 + 88*x^26 + 19*x^25 + 24*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 72*x^18 + 35*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 113*x^9 + 40*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 120*x^2 + 89*x + 120, x^29 + 106*x^27 + 72*x^26 + 3*x^25 + 88*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 24*x^18 + 51*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + x^9 + 104*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 40*x^2 + 73*x + 56, x^29 + 106*x^27 + 40*x^26 + 83*x^25 + 104*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 56*x^18 + 99*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 49*x^9 + 88*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 8*x^2 + 25*x + 8, x^29 + 106*x^27 + 56*x^26 + 19*x^25 + 88*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 104*x^18 + 35*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 113*x^9 + 104*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 88*x^2 + 89*x + 56, x^29 + 106*x^27 + 32*x^26 + 19*x^25 + 64*x^24 + 36*x^23 + 57*x^21 + 64*x^20 + 86*x^19 + 32*x^18 + 99*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 113*x^9 + 64*x^8 + 36*x^7 + 43*x^5 + 64*x^4 + 10*x^3 + 96*x^2 + 25*x, x^29 + 106*x^27 + 36*x^26 + 43*x^25 + 100*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 108*x^18 + 11*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 89*x^9 + 60*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 52*x^2 + 113*x + 20, x^29 + 106*x^27 + 64*x^26 + 67*x^25 + 112*x^24 + 36*x^23 + 89*x^21 + 32*x^20 + 86*x^19 + 64*x^18 + 115*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 65*x^9 + 16*x^8 + 36*x^7 + 75*x^5 + 32*x^4 + 10*x^3 + 64*x^2 + 9*x + 48, x^29 + 106*x^27 + 64*x^26 + 83*x^25 + 64*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 86*x^19 + 35*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 49*x^9 + 64*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 10*x^3 + 89*x, x^29 + 106*x^27 + 56*x^26 + 115*x^25 + 56*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 104*x^18 + 67*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 17*x^9 + 8*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 88*x^2 + 57*x + 24, x^29 + 106*x^27 + 60*x^26 + 75*x^25 + 92*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 52*x^18 + 107*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 57*x^9 + 4*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 44*x^2 + 17*x + 44, x^29 + 106*x^27 + 3*x^25 + 80*x^24 + 36*x^23 + 89*x^21 + 96*x^20 + 86*x^19 + 51*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + x^9 + 48*x^8 + 36*x^7 + 75*x^5 + 96*x^4 + 10*x^3 + 73*x + 16, x^29 + 106*x^27 + 108*x^26 + 107*x^25 + 76*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 68*x^18 + 75*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 25*x^9 + 20*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 28*x^2 + 49*x + 92, x^29 + 106*x^27 + 60*x^26 + 43*x^25 + 92*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 116*x^18 + 75*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 89*x^9 + 4*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 108*x^2 + 49*x + 108, x^29 + 106*x^27 + 84*x^26 + 43*x^25 + 52*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 60*x^18 + 75*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 89*x^9 + 108*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 100*x^2 + 49*x + 100, x^29 + 106*x^27 + 19*x^25 + 64*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 86*x^19 + 64*x^18 + 99*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 113*x^9 + 64*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 10*x^3 + 64*x^2 + 25*x, x^29 + 106*x^27 + 3*x^25 + 48*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 22*x^19 + 64*x^18 + 115*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + x^9 + 80*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 74*x^3 + 64*x^2 + 9*x + 48, x^29 + 106*x^27 + 48*x^26 + 83*x^25 + 112*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 16*x^18 + 99*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 49*x^9 + 16*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 112*x^2 + 25*x + 48, x^29 + 106*x^27 + 116*x^26 + 11*x^25 + 116*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 92*x^18 + 43*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 121*x^9 + 44*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 68*x^2 + 81*x + 100, x^29 + 106*x^27 + 56*x^26 + 3*x^25 + 8*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 40*x^18 + 115*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + x^9 + 56*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 24*x^2 + 9*x + 104, x^29 + 106*x^27 + 68*x^26 + 59*x^25 + 20*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 12*x^18 + 59*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 73*x^9 + 12*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 20*x^2 + 65*x + 68, x^29 + 106*x^27 + 76*x^26 + 27*x^25 + 28*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 100*x^18 + 27*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 105*x^9 + 68*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 124*x^2 + 97*x + 108, x^29 + 106*x^27 + 116*x^26 + 107*x^25 + 20*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 28*x^18 + 11*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 25*x^9 + 12*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 4*x^2 + 113*x + 68, x^29 + 106*x^27 + 52*x^26 + 27*x^25 + 68*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 28*x^18 + 27*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 105*x^9 + 92*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 4*x^2 + 97*x + 116, x^29 + 106*x^27 + 36*x^26 + 91*x^25 + 84*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 108*x^18 + 91*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 41*x^9 + 76*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 52*x^2 + 33*x + 68, x^29 + 106*x^27 + 4*x^26 + 107*x^25 + 100*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 76*x^18 + 11*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 25*x^9 + 60*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 84*x^2 + 113*x + 84, x^29 + 106*x^27 + 28*x^26 + 107*x^25 + 28*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 20*x^18 + 11*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 25*x^9 + 68*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 76*x^2 + 113*x + 44, x^29 + 106*x^27 + 32*x^26 + 19*x^25 + 96*x^24 + 36*x^23 + 57*x^21 + 86*x^19 + 32*x^18 + 99*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 113*x^9 + 32*x^8 + 36*x^7 + 43*x^5 + 10*x^3 + 96*x^2 + 25*x + 32, x^29 + 106*x^27 + 96*x^26 + 99*x^25 + 48*x^24 + 100*x^23 + 89*x^21 + 96*x^20 + 22*x^19 + 96*x^18 + 19*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 33*x^9 + 80*x^8 + 100*x^7 + 75*x^5 + 96*x^4 + 74*x^3 + 32*x^2 + 105*x + 48, x^29 + 106*x^27 + 104*x^26 + 83*x^25 + 104*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 56*x^18 + 35*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 49*x^9 + 88*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 8*x^2 + 89*x + 72, x^29 + 106*x^27 + 4*x^26 + 75*x^25 + 68*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 12*x^18 + 107*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 57*x^9 + 92*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 20*x^2 + 17*x + 116, x^29 + 106*x^27 + 36*x^26 + 107*x^25 + 100*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 108*x^18 + 75*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 25*x^9 + 60*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 52*x^2 + 49*x + 20, x^29 + 106*x^27 + 68*x^26 + 75*x^25 + 4*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 76*x^18 + 107*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 57*x^9 + 28*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 84*x^2 + 17*x + 52, x^29 + 106*x^27 + 92*x^26 + 27*x^25 + 12*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 20*x^18 + 27*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 105*x^9 + 84*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 76*x^2 + 97*x + 28, x^29 + 106*x^27 + 104*x^26 + 19*x^25 + 8*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 120*x^18 + 35*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 113*x^9 + 56*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 72*x^2 + 89*x + 40, x^29 + 106*x^27 + 16*x^26 + 35*x^25 + 32*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 22*x^19 + 112*x^18 + 83*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 97*x^9 + 96*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 74*x^3 + 16*x^2 + 41*x + 96, x^29 + 106*x^27 + 80*x^26 + 83*x^25 + 80*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 112*x^18 + 99*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 49*x^9 + 48*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 16*x^2 + 25*x + 16, x^29 + 106*x^27 + 76*x^26 + 11*x^25 + 44*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 36*x^18 + 107*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 121*x^9 + 52*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 60*x^2 + 17*x + 124, x^29 + 106*x^27 + 24*x^26 + 35*x^25 + 8*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 8*x^18 + 19*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 97*x^9 + 56*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 56*x^2 + 105*x + 40, x^29 + 106*x^27 + 60*x^26 + 75*x^25 + 60*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 52*x^18 + 107*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 57*x^9 + 36*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 44*x^2 + 17*x + 12, x^29 + 106*x^27 + 52*x^26 + 11*x^25 + 52*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 92*x^18 + 107*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 121*x^9 + 108*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 68*x^2 + 17*x + 100, x^29 + 106*x^27 + 124*x^26 + 91*x^25 + 76*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 116*x^18 + 91*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 41*x^9 + 20*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 108*x^2 + 33*x + 92, x^29 + 106*x^27 + 60*x^26 + 27*x^25 + 12*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 52*x^18 + 27*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 105*x^9 + 84*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 44*x^2 + 97*x + 28, x^29 + 106*x^27 + 96*x^26 + 35*x^25 + 112*x^24 + 100*x^23 + 89*x^21 + 96*x^20 + 22*x^19 + 96*x^18 + 83*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 97*x^9 + 16*x^8 + 100*x^7 + 75*x^5 + 96*x^4 + 74*x^3 + 32*x^2 + 41*x + 112, x^29 + 106*x^27 + 36*x^26 + 27*x^25 + 116*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 44*x^18 + 91*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 105*x^9 + 44*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 116*x^2 + 33*x + 36, x^29 + 106*x^27 + 64*x^26 + 35*x^25 + 112*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 22*x^19 + 83*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 97*x^9 + 16*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 74*x^3 + 41*x + 112, x^29 + 106*x^27 + 12*x^26 + 27*x^25 + 124*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 36*x^18 + 27*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 105*x^9 + 100*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 60*x^2 + 97*x + 76, x^29 + 106*x^27 + 80*x^26 + 51*x^25 + 80*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 48*x^18 + 67*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 81*x^9 + 48*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 80*x^2 + 57*x + 80, x^29 + 106*x^27 + 4*x^26 + 91*x^25 + 20*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 76*x^18 + 27*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 41*x^9 + 12*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 84*x^2 + 97*x + 68, x^29 + 106*x^27 + 35*x^25 + 112*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 22*x^19 + 64*x^18 + 83*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 97*x^9 + 16*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 74*x^3 + 64*x^2 + 41*x + 112, x^29 + 106*x^27 + 16*x^26 + 99*x^25 + 64*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 86*x^19 + 48*x^18 + 83*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 33*x^9 + 64*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 10*x^3 + 80*x^2 + 41*x + 64, x^29 + 106*x^27 + 12*x^26 + 75*x^25 + 76*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 36*x^18 + 107*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 57*x^9 + 20*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 60*x^2 + 17*x + 92, x^29 + 106*x^27 + 8*x^26 + 3*x^25 + 120*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 24*x^18 + 115*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + x^9 + 72*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 40*x^2 + 9*x + 24, x^29 + 106*x^27 + 44*x^26 + 27*x^25 + 60*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 4*x^18 + 27*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 105*x^9 + 36*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 92*x^2 + 97*x + 12, x^29 + 106*x^27 + 36*x^26 + 75*x^25 + 4*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 44*x^18 + 43*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 57*x^9 + 28*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 116*x^2 + 81*x + 116, x^29 + 106*x^27 + 36*x^26 + 59*x^25 + 116*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 44*x^18 + 59*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 73*x^9 + 44*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 116*x^2 + 65*x + 36, x^29 + 106*x^27 + 16*x^26 + 115*x^25 + 16*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 48*x^18 + 67*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 17*x^9 + 112*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 80*x^2 + 57*x + 80, x^29 + 106*x^27 + 16*x^26 + 67*x^25 + 100*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 112*x^18 + 51*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 65*x^9 + 100*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 16*x^2 + 73*x + 64, x^29 + 106*x^27 + 44*x^26 + 11*x^25 + 76*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 68*x^18 + 107*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 121*x^9 + 20*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 28*x^2 + 17*x + 28, x^29 + 106*x^27 + 124*x^26 + 91*x^25 + 108*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 52*x^18 + 27*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 41*x^9 + 116*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 44*x^2 + 97*x + 60, x^29 + 106*x^27 + 36*x^26 + 43*x^25 + 4*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 44*x^18 + 75*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 89*x^9 + 28*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 116*x^2 + 49*x + 116, x^29 + 106*x^27 + 19*x^25 + 96*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 86*x^19 + 64*x^18 + 99*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 113*x^9 + 32*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 10*x^3 + 64*x^2 + 25*x + 32, x^29 + 106*x^27 + 64*x^26 + 83*x^25 + 96*x^24 + 100*x^23 + 121*x^21 + 64*x^20 + 22*x^19 + 64*x^18 + 99*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 49*x^9 + 32*x^8 + 100*x^7 + 107*x^5 + 64*x^4 + 74*x^3 + 64*x^2 + 25*x + 96, x^29 + 106*x^27 + 80*x^26 + 115*x^25 + 112*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 48*x^18 + 3*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 17*x^9 + 16*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 80*x^2 + 121*x + 112, x^29 + 106*x^27 + 40*x^26 + 115*x^25 + 104*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 56*x^18 + 67*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 17*x^9 + 88*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 8*x^2 + 57*x + 8, x^29 + 106*x^27 + 24*x^26 + 51*x^25 + 24*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 72*x^18 + 67*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 81*x^9 + 40*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 120*x^2 + 57*x + 56, x^29 + 106*x^27 + 20*x^26 + 107*x^25 + 116*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 60*x^18 + 75*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 25*x^9 + 44*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 100*x^2 + 49*x + 100, x^29 + 106*x^27 + 68*x^26 + 123*x^25 + 84*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 76*x^18 + 59*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 9*x^9 + 76*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 84*x^2 + 65*x + 68, x^29 + 106*x^27 + 16*x^26 + 99*x^25 + 96*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 22*x^19 + 112*x^18 + 19*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 33*x^9 + 32*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 74*x^3 + 16*x^2 + 105*x + 32, x^29 + 106*x^27 + 72*x^26 + 19*x^25 + 104*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 24*x^18 + 35*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 113*x^9 + 88*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 40*x^2 + 89*x + 8, x^29 + 106*x^27 + 56*x^26 + 19*x^25 + 88*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 40*x^18 + 99*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 113*x^9 + 104*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 24*x^2 + 25*x + 120, x^29 + 106*x^27 + 52*x^26 + 43*x^25 + 116*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 92*x^18 + 75*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 89*x^9 + 44*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 68*x^2 + 49*x + 36, x^29 + 106*x^27 + 84*x^26 + 91*x^25 + 36*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 124*x^18 + 91*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 41*x^9 + 124*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 36*x^2 + 33*x + 84, x^29 + 106*x^27 + 32*x^26 + 35*x^25 + 80*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 86*x^19 + 96*x^18 + 19*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 97*x^9 + 48*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 10*x^3 + 32*x^2 + 105*x + 16, x^29 + 106*x^27 + 28*x^26 + 91*x^25 + 44*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 84*x^18 + 91*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 41*x^9 + 52*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 12*x^2 + 33*x + 60, x^29 + 106*x^27 + 120*x^26 + 67*x^25 + 104*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 104*x^18 + 51*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 65*x^9 + 88*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 88*x^2 + 73*x + 72, x^29 + 106*x^27 + 36*x^26 + 91*x^25 + 20*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 108*x^18 + 91*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 41*x^9 + 12*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 52*x^2 + 33*x + 4, x^29 + 106*x^27 + 96*x^26 + 35*x^25 + 48*x^24 + 100*x^23 + 89*x^21 + 96*x^20 + 22*x^19 + 96*x^18 + 83*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 97*x^9 + 80*x^8 + 100*x^7 + 75*x^5 + 96*x^4 + 74*x^3 + 32*x^2 + 41*x + 48, x^29 + 106*x^27 + 64*x^26 + 35*x^25 + 48*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 22*x^19 + 83*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 97*x^9 + 80*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 74*x^3 + 41*x + 48, x^29 + 106*x^27 + 12*x^26 + 59*x^25 + 92*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 100*x^18 + 59*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 73*x^9 + 4*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 124*x^2 + 65*x + 108, x^29 + 106*x^27 + 8*x^26 + 35*x^25 + 120*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 88*x^18 + 19*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 97*x^9 + 72*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 104*x^2 + 105*x + 88, x^29 + 106*x^27 + 112*x^26 + 83*x^25 + 16*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 16*x^18 + 35*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 49*x^9 + 112*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 112*x^2 + 89*x + 16, x^29 + 106*x^27 + 35*x^25 + 48*x^24 + 100*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 22*x^19 + 64*x^18 + 83*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 97*x^9 + 80*x^8 + 100*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 74*x^3 + 64*x^2 + 41*x + 48, x^29 + 106*x^27 + 72*x^26 + 99*x^25 + 120*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 24*x^18 + 83*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 33*x^9 + 72*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 40*x^2 + 41*x + 88, x^29 + 106*x^27 + 96*x^26 + 3*x^25 + 112*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 86*x^19 + 32*x^18 + 51*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + x^9 + 16*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 10*x^3 + 96*x^2 + 73*x + 48, x^29 + 106*x^27 + 124*x^26 + 27*x^25 + 12*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 52*x^18 + 91*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 105*x^9 + 84*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 44*x^2 + 33*x + 92, x^29 + 106*x^27 + 104*x^26 + 115*x^25 + 104*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 56*x^18 + 3*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 17*x^9 + 88*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 8*x^2 + 121*x + 72, x^29 + 106*x^27 + 88*x^26 + 83*x^25 + 24*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 8*x^18 + 35*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 49*x^9 + 40*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 56*x^2 + 89*x + 56, x^29 + 106*x^27 + 60*x^26 + 43*x^25 + 28*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 52*x^18 + 11*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 89*x^9 + 68*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 44*x^2 + 113*x + 108, x^29 + 106*x^27 + 80*x^26 + 3*x^25 + 100*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 48*x^18 + 115*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + x^9 + 100*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 80*x^2 + 9*x + 64, x^29 + 106*x^27 + 20*x^26 + 123*x^25 + 68*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 60*x^18 + 59*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 9*x^9 + 92*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 100*x^2 + 65*x + 116, x^29 + 106*x^27 + 56*x^26 + 51*x^25 + 120*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 104*x^18 + 3*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 81*x^9 + 72*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 88*x^2 + 121*x + 88, x^29 + 106*x^27 + 120*x^26 + 3*x^25 + 8*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 40*x^18 + 51*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + x^9 + 56*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 24*x^2 + 73*x + 40, x^29 + 106*x^27 + 96*x^26 + 51*x^25 + 96*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 22*x^19 + 32*x^18 + 3*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 81*x^9 + 32*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 74*x^3 + 96*x^2 + 121*x + 96, x^29 + 106*x^27 + 68*x^26 + 27*x^25 + 116*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 76*x^18 + 27*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 105*x^9 + 44*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 84*x^2 + 97*x + 100, x^29 + 106*x^27 + 32*x^26 + 3*x^25 + 112*x^24 + 100*x^23 + 25*x^21 + 96*x^20 + 22*x^19 + 32*x^18 + 115*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + x^9 + 16*x^8 + 100*x^7 + 11*x^5 + 96*x^4 + 74*x^3 + 96*x^2 + 9*x + 112, x^29 + 106*x^27 + 116*x^26 + 123*x^25 + 68*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 28*x^18 + 123*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 9*x^9 + 92*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 4*x^2 + x + 52, x^29 + 106*x^27 + 16*x^26 + 19*x^25 + 80*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 112*x^18 + 99*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 113*x^9 + 48*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 16*x^2 + 25*x + 80, x^29 + 106*x^27 + 84*x^26 + 27*x^25 + 100*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 124*x^18 + 27*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 105*x^9 + 60*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 36*x^2 + 97*x + 20, x^29 + 106*x^27 + 12*x^26 + 107*x^25 + 108*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 100*x^18 + 11*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 25*x^9 + 116*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 124*x^2 + 113*x + 60, x^29 + 106*x^27 + 92*x^26 + 27*x^25 + 44*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 84*x^18 + 91*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 105*x^9 + 52*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 12*x^2 + 33*x + 124, x^29 + 106*x^27 + 120*x^26 + 83*x^25 + 24*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 104*x^18 + 35*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 49*x^9 + 40*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 88*x^2 + 89*x + 56, x^29 + 106*x^27 + 32*x^26 + 115*x^25 + 36*x^23 + 121*x^21 + 64*x^20 + 86*x^19 + 32*x^18 + 3*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 17*x^9 + 36*x^7 + 107*x^5 + 64*x^4 + 10*x^3 + 96*x^2 + 121*x + 64, x^29 + 106*x^27 + 68*x^26 + 43*x^25 + 68*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 76*x^18 + 11*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 89*x^9 + 92*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 84*x^2 + 113*x + 116, x^29 + 106*x^27 + 100*x^26 + 11*x^25 + 4*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 108*x^18 + 107*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 121*x^9 + 28*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 52*x^2 + 17*x + 116, x^29 + 106*x^27 + 124*x^26 + 91*x^25 + 12*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 52*x^18 + 27*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 41*x^9 + 84*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 44*x^2 + 97*x + 92, x^29 + 106*x^27 + 64*x^26 + 115*x^25 + 36*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 86*x^19 + 3*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 17*x^9 + 36*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 10*x^3 + 121*x + 64, x^29 + 106*x^27 + 84*x^26 + 11*x^25 + 116*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 124*x^18 + 43*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 121*x^9 + 44*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 36*x^2 + 81*x + 100, x^29 + 106*x^27 + 8*x^26 + 67*x^25 + 56*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 88*x^18 + 115*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 65*x^9 + 8*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 104*x^2 + 9*x + 24, x^29 + 106*x^27 + 12*x^26 + 11*x^25 + 76*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 100*x^18 + 107*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 121*x^9 + 20*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 124*x^2 + 17*x + 28, x^29 + 106*x^27 + 115*x^25 + 36*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 86*x^19 + 64*x^18 + 3*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 17*x^9 + 36*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 10*x^3 + 64*x^2 + 121*x + 64, x^29 + 106*x^27 + 40*x^26 + 83*x^25 + 40*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 120*x^18 + 35*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 49*x^9 + 24*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 72*x^2 + 89*x + 8, x^29 + 106*x^27 + 48*x^26 + 99*x^25 + 64*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 86*x^19 + 16*x^18 + 83*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 33*x^9 + 64*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 10*x^3 + 112*x^2 + 41*x + 64, x^29 + 106*x^27 + 68*x^26 + 43*x^25 + 4*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 12*x^18 + 75*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 89*x^9 + 28*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 20*x^2 + 49*x + 116, x^29 + 106*x^27 + 36*x^26 + 91*x^25 + 52*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 44*x^18 + 27*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 41*x^9 + 108*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 116*x^2 + 97*x + 100, x^29 + 106*x^27 + 108*x^26 + 59*x^25 + 28*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 68*x^18 + 123*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 73*x^9 + 68*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 28*x^2 + x + 108, x^29 + 106*x^27 + 40*x^26 + 99*x^25 + 120*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 120*x^18 + 19*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 33*x^9 + 72*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 72*x^2 + 105*x + 24, x^29 + 106*x^27 + 88*x^26 + 83*x^25 + 88*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 8*x^18 + 35*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 49*x^9 + 104*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 56*x^2 + 89*x + 120, x^29 + 106*x^27 + 72*x^26 + 51*x^25 + 40*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 88*x^18 + 67*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 81*x^9 + 24*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 104*x^2 + 57*x + 8, x^29 + 106*x^27 + 4*x^26 + 11*x^25 + 68*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 12*x^18 + 43*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 121*x^9 + 92*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 20*x^2 + 81*x + 116, x^29 + 106*x^27 + 68*x^26 + 59*x^25 + 20*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 76*x^18 + 123*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 73*x^9 + 12*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 84*x^2 + x + 4, x^29 + 106*x^27 + 20*x^26 + 43*x^25 + 52*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 60*x^18 + 11*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 89*x^9 + 108*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 100*x^2 + 113*x + 36, x^29 + 106*x^27 + 124*x^26 + 123*x^25 + 44*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 52*x^18 + 123*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 9*x^9 + 52*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 44*x^2 + x + 124, x^29 + 106*x^27 + 4*x^26 + 107*x^25 + 36*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 12*x^18 + 75*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 25*x^9 + 124*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 20*x^2 + 49*x + 84, x^29 + 106*x^27 + 56*x^26 + 83*x^25 + 24*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 104*x^18 + 99*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 49*x^9 + 40*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 88*x^2 + 25*x + 120, x^29 + 106*x^27 + 96*x^26 + 51*x^25 + 100*x^23 + 64*x^22 + 57*x^21 + 22*x^19 + 32*x^18 + 3*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 81*x^9 + 100*x^7 + 64*x^6 + 43*x^5 + 74*x^3 + 96*x^2 + 121*x, x^29 + 106*x^27 + 112*x^26 + 115*x^25 + 48*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 80*x^18 + 67*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 17*x^9 + 80*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 48*x^2 + 57*x + 112, x^29 + 106*x^27 + 76*x^26 + 75*x^25 + 108*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 36*x^18 + 43*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 57*x^9 + 116*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 60*x^2 + 81*x + 60, x^29 + 106*x^27 + 16*x^26 + 83*x^25 + 80*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 112*x^18 + 35*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 49*x^9 + 48*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 16*x^2 + 89*x + 80, x^29 + 106*x^27 + 104*x^26 + 67*x^25 + 88*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 56*x^18 + 51*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 65*x^9 + 104*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 8*x^2 + 73*x + 120, x^29 + 106*x^27 + 40*x^26 + 3*x^25 + 24*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 120*x^18 + 115*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + x^9 + 40*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 72*x^2 + 9*x + 56, x^29 + 106*x^27 + 8*x^26 + 51*x^25 + 104*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 24*x^18 + 67*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 81*x^9 + 88*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 40*x^2 + 57*x + 72, x^29 + 106*x^27 + 52*x^26 + 43*x^25 + 52*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 92*x^18 + 75*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 89*x^9 + 108*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 68*x^2 + 49*x + 100, x^29 + 106*x^27 + 40*x^26 + 19*x^25 + 8*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 120*x^18 + 99*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 113*x^9 + 56*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 72*x^2 + 25*x + 104, x^29 + 106*x^27 + 24*x^26 + 115*x^25 + 88*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 72*x^18 + 3*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 17*x^9 + 104*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 120*x^2 + 121*x + 120, x^29 + 106*x^27 + 60*x^26 + 107*x^25 + 60*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 52*x^18 + 75*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 25*x^9 + 36*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 44*x^2 + 49*x + 12, x^29 + 106*x^27 + 84*x^26 + 123*x^25 + 36*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 124*x^18 + 59*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 9*x^9 + 124*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 36*x^2 + 65*x + 84, x^29 + 106*x^27 + 20*x^26 + 75*x^25 + 20*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 124*x^18 + 43*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 57*x^9 + 12*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 36*x^2 + 81*x + 68, x^29 + 106*x^27 + 92*x^26 + 107*x^25 + 124*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 84*x^18 + 11*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 25*x^9 + 100*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 12*x^2 + 113*x + 12, x^29 + 106*x^27 + 100*x^26 + 107*x^25 + 100*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 108*x^18 + 11*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 25*x^9 + 60*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 52*x^2 + 113*x + 84, x^29 + 106*x^27 + 104*x^26 + 99*x^25 + 120*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 120*x^18 + 83*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 33*x^9 + 72*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 72*x^2 + 41*x + 88, x^29 + 106*x^27 + 12*x^26 + 59*x^25 + 92*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 36*x^18 + 123*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 73*x^9 + 4*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 60*x^2 + x + 44, x^29 + 106*x^27 + 80*x^26 + 35*x^25 + 96*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 22*x^19 + 48*x^18 + 83*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 97*x^9 + 32*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 74*x^3 + 80*x^2 + 41*x + 32, x^29 + 106*x^27 + 56*x^26 + 3*x^25 + 72*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 40*x^18 + 115*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + x^9 + 120*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 24*x^2 + 9*x + 40, x^29 + 106*x^27 + 124*x^26 + 91*x^25 + 76*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 52*x^18 + 27*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 41*x^9 + 20*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 44*x^2 + 97*x + 28, x^29 + 106*x^27 + 100*x^26 + 27*x^25 + 116*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 44*x^18 + 27*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 105*x^9 + 44*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 116*x^2 + 97*x + 100, x^29 + 106*x^27 + 96*x^26 + 19*x^25 + 32*x^24 + 36*x^23 + 57*x^21 + 86*x^19 + 96*x^18 + 99*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 113*x^9 + 96*x^8 + 36*x^7 + 43*x^5 + 10*x^3 + 32*x^2 + 25*x + 96, x^29 + 106*x^27 + 124*x^26 + 123*x^25 + 108*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 52*x^18 + 123*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 9*x^9 + 116*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 44*x^2 + x + 60, x^29 + 106*x^27 + 112*x^26 + 83*x^25 + 112*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 80*x^18 + 99*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 49*x^9 + 16*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 48*x^2 + 25*x + 48, x^29 + 106*x^27 + 12*x^26 + 11*x^25 + 12*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 100*x^18 + 107*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 121*x^9 + 84*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 124*x^2 + 17*x + 92, x^29 + 106*x^27 + 120*x^26 + 19*x^25 + 56*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 40*x^18 + 35*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 113*x^9 + 8*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 24*x^2 + 89*x + 24, x^29 + 106*x^27 + 92*x^26 + 59*x^25 + 76*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 20*x^18 + 123*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 73*x^9 + 20*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 76*x^2 + x + 92, x^29 + 106*x^27 + 52*x^26 + 107*x^25 + 116*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 92*x^18 + 11*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 25*x^9 + 44*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 68*x^2 + 113*x + 36, x^29 + 106*x^27 + 4*x^26 + 75*x^25 + 100*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 76*x^18 + 43*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 57*x^9 + 60*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 84*x^2 + 81*x + 84, x^29 + 106*x^27 + 120*x^26 + 83*x^25 + 24*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 40*x^18 + 99*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 49*x^9 + 40*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 24*x^2 + 25*x + 120, x^29 + 106*x^27 + 124*x^26 + 59*x^25 + 12*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 52*x^18 + 59*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 73*x^9 + 84*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 44*x^2 + 65*x + 92, x^29 + 106*x^27 + 116*x^26 + 91*x^25 + 4*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 92*x^18 + 91*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 41*x^9 + 28*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 68*x^2 + 33*x + 52, x^29 + 106*x^27 + 16*x^26 + 35*x^25 + 100*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 112*x^18 + 83*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 97*x^9 + 100*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 16*x^2 + 41*x + 64, x^29 + 106*x^27 + 44*x^26 + 91*x^25 + 28*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 4*x^18 + 91*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 41*x^9 + 68*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 92*x^2 + 33*x + 108, x^29 + 106*x^27 + 104*x^26 + 3*x^25 + 120*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 56*x^18 + 115*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + x^9 + 72*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 8*x^2 + 9*x + 24, x^29 + 106*x^27 + 48*x^26 + 115*x^25 + 112*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 80*x^18 + 3*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 17*x^9 + 16*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 48*x^2 + 121*x + 112, x^29 + 106*x^27 + 36*x^26 + 43*x^25 + 68*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 108*x^18 + 11*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 89*x^9 + 92*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 52*x^2 + 113*x + 116, x^29 + 106*x^27 + 92*x^26 + 27*x^25 + 76*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 20*x^18 + 27*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 105*x^9 + 20*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 76*x^2 + 97*x + 92, x^29 + 106*x^27 + 12*x^26 + 75*x^25 + 12*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 100*x^18 + 43*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 57*x^9 + 84*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 124*x^2 + 81*x + 92, x^29 + 106*x^27 + 72*x^26 + 115*x^25 + 72*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 24*x^18 + 67*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 17*x^9 + 120*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 40*x^2 + 57*x + 104, x^29 + 106*x^27 + 16*x^26 + 67*x^25 + 96*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 22*x^19 + 112*x^18 + 51*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 65*x^9 + 32*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 74*x^3 + 16*x^2 + 73*x + 32, x^29 + 106*x^27 + 4*x^26 + 27*x^25 + 84*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 76*x^18 + 91*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 105*x^9 + 76*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 84*x^2 + 33*x + 4, x^29 + 106*x^27 + 8*x^26 + 35*x^25 + 24*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 24*x^18 + 83*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 97*x^9 + 40*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 40*x^2 + 41*x + 56, x^29 + 106*x^27 + 56*x^26 + 3*x^25 + 40*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 40*x^18 + 115*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + x^9 + 24*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 24*x^2 + 9*x + 8, x^29 + 106*x^27 + 88*x^26 + 19*x^25 + 120*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 72*x^18 + 35*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 113*x^9 + 72*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 120*x^2 + 89*x + 88, x^29 + 106*x^27 + 96*x^26 + 67*x^25 + 80*x^24 + 100*x^23 + 25*x^21 + 32*x^20 + 22*x^19 + 96*x^18 + 51*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 65*x^9 + 48*x^8 + 100*x^7 + 11*x^5 + 32*x^4 + 74*x^3 + 32*x^2 + 73*x + 80, x^29 + 106*x^27 + 56*x^26 + 19*x^25 + 120*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 104*x^18 + 35*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 113*x^9 + 72*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 88*x^2 + 89*x + 88, x^29 + 106*x^27 + 24*x^26 + 67*x^25 + 40*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 72*x^18 + 51*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 65*x^9 + 24*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 120*x^2 + 73*x + 8, x^29 + 106*x^27 + 20*x^26 + 91*x^25 + 100*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 124*x^18 + 27*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 41*x^9 + 60*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 36*x^2 + 97*x + 84, x^29 + 106*x^27 + 100*x^26 + 107*x^25 + 68*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 108*x^18 + 11*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 25*x^9 + 92*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 52*x^2 + 113*x + 52, x^29 + 106*x^27 + 76*x^26 + 107*x^25 + 12*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 100*x^18 + 75*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 25*x^9 + 84*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 124*x^2 + 49*x + 28, x^29 + 106*x^27 + 8*x^26 + 67*x^25 + 56*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 24*x^18 + 51*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 65*x^9 + 8*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 40*x^2 + 73*x + 88, x^29 + 106*x^27 + 28*x^26 + 75*x^25 + 28*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 84*x^18 + 107*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 57*x^9 + 68*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 12*x^2 + 17*x + 108, x^29 + 106*x^27 + 8*x^26 + 99*x^25 + 120*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 24*x^18 + 19*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 33*x^9 + 72*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 40*x^2 + 105*x + 24, x^29 + 106*x^27 + 16*x^26 + 83*x^25 + 16*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 48*x^18 + 99*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 49*x^9 + 112*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 80*x^2 + 25*x + 80, x^29 + 106*x^27 + 56*x^26 + 51*x^25 + 88*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 40*x^18 + 67*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 81*x^9 + 104*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 24*x^2 + 57*x + 120, x^29 + 106*x^27 + 124*x^26 + 107*x^25 + 28*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 116*x^18 + 75*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 25*x^9 + 68*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 108*x^2 + 49*x + 108, x^29 + 106*x^27 + 124*x^26 + 107*x^25 + 28*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 52*x^18 + 11*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 25*x^9 + 68*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 44*x^2 + 113*x + 44, x^29 + 106*x^27 + 8*x^26 + 83*x^25 + 72*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 24*x^18 + 35*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 49*x^9 + 120*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 40*x^2 + 89*x + 40, x^29 + 106*x^27 + 83*x^25 + 32*x^24 + 100*x^23 + 121*x^21 + 64*x^20 + 22*x^19 + 99*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 49*x^9 + 96*x^8 + 100*x^7 + 107*x^5 + 64*x^4 + 74*x^3 + 25*x + 32, x^29 + 106*x^27 + 92*x^26 + 27*x^25 + 44*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 20*x^18 + 27*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 105*x^9 + 52*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 76*x^2 + 97*x + 60, x^29 + 106*x^27 + 36*x^26 + 107*x^25 + 68*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 108*x^18 + 75*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 25*x^9 + 92*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 52*x^2 + 49*x + 116, x^29 + 106*x^27 + 12*x^26 + 91*x^25 + 28*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 100*x^18 + 27*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 41*x^9 + 68*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 124*x^2 + 97*x + 44, x^29 + 106*x^27 + 80*x^26 + 3*x^25 + 96*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 22*x^19 + 48*x^18 + 115*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + x^9 + 32*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 74*x^3 + 80*x^2 + 9*x + 32, x^29 + 106*x^27 + 68*x^26 + 75*x^25 + 100*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 76*x^18 + 107*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 57*x^9 + 60*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 84*x^2 + 17*x + 20, x^29 + 106*x^27 + 40*x^26 + 35*x^25 + 24*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 120*x^18 + 83*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 97*x^9 + 40*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 72*x^2 + 41*x + 56, x^29 + 106*x^27 + 24*x^26 + 99*x^25 + 72*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 8*x^18 + 83*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 33*x^9 + 120*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 56*x^2 + 41*x + 104, x^29 + 106*x^27 + 20*x^26 + 59*x^25 + 36*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 60*x^18 + 123*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 73*x^9 + 124*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 100*x^2 + x + 84, x^29 + 106*x^27 + 68*x^26 + 107*x^25 + 100*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 12*x^18 + 11*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 25*x^9 + 60*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 20*x^2 + 113*x + 84, x^29 + 106*x^27 + 24*x^26 + 115*x^25 + 120*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 8*x^18 + 67*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 17*x^9 + 72*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 56*x^2 + 57*x + 88, x^29 + 106*x^27 + 12*x^26 + 59*x^25 + 124*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 100*x^18 + 59*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 73*x^9 + 100*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 124*x^2 + 65*x + 12, x^29 + 106*x^27 + 72*x^26 + 3*x^25 + 120*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 24*x^18 + 51*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + x^9 + 72*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 40*x^2 + 73*x + 88, x^29 + 106*x^27 + 4*x^26 + 123*x^25 + 116*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 12*x^18 + 59*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 9*x^9 + 44*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 20*x^2 + 65*x + 100, x^29 + 106*x^27 + 120*x^26 + 99*x^25 + 40*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 104*x^18 + 19*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 33*x^9 + 24*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 88*x^2 + 105*x + 8, x^29 + 106*x^27 + 96*x^26 + 19*x^25 + 100*x^23 + 64*x^22 + 121*x^21 + 22*x^19 + 32*x^18 + 35*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 113*x^9 + 100*x^7 + 64*x^6 + 107*x^5 + 74*x^3 + 96*x^2 + 89*x, x^29 + 106*x^27 + 84*x^26 + 91*x^25 + 36*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 60*x^18 + 27*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 41*x^9 + 124*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 100*x^2 + 97*x + 20, x^29 + 106*x^27 + 52*x^26 + 91*x^25 + 4*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 28*x^18 + 91*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 41*x^9 + 28*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 4*x^2 + 33*x + 52, x^29 + 106*x^27 + 4*x^26 + 59*x^25 + 52*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 76*x^18 + 59*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 73*x^9 + 108*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 84*x^2 + 65*x + 100, x^29 + 106*x^27 + 108*x^26 + 91*x^25 + 92*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 4*x^18 + 27*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 41*x^9 + 4*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 92*x^2 + 97*x + 108, x^29 + 106*x^27 + 32*x^26 + 115*x^25 + 96*x^24 + 36*x^23 + 121*x^21 + 86*x^19 + 32*x^18 + 3*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 17*x^9 + 32*x^8 + 36*x^7 + 107*x^5 + 10*x^3 + 96*x^2 + 121*x + 32, x^29 + 106*x^27 + 92*x^26 + 123*x^25 + 12*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 84*x^18 + 123*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 9*x^9 + 84*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 12*x^2 + x + 92, x^29 + 106*x^27 + 76*x^26 + 59*x^25 + 92*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 36*x^18 + 59*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 73*x^9 + 4*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 60*x^2 + 65*x + 108, x^29 + 106*x^27 + 64*x^26 + 115*x^25 + 96*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 86*x^19 + 3*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 17*x^9 + 32*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 10*x^3 + 121*x + 32, x^29 + 106*x^27 + 104*x^26 + 67*x^25 + 88*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 120*x^18 + 115*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 65*x^9 + 104*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 72*x^2 + 9*x + 56, x^29 + 106*x^27 + 116*x^26 + 75*x^25 + 84*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 92*x^18 + 107*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 57*x^9 + 76*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 68*x^2 + 17*x + 68, x^29 + 106*x^27 + 120*x^26 + 83*x^25 + 120*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 104*x^18 + 35*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 49*x^9 + 72*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 88*x^2 + 89*x + 24, x^29 + 106*x^27 + 115*x^25 + 96*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 86*x^19 + 64*x^18 + 3*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 17*x^9 + 32*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 10*x^3 + 64*x^2 + 121*x + 32, x^29 + 106*x^27 + 120*x^26 + 115*x^25 + 88*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 104*x^18 + 3*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 17*x^9 + 104*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 88*x^2 + 121*x + 120, x^29 + 106*x^27 + 32*x^26 + 19*x^25 + 32*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 22*x^19 + 96*x^18 + 35*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 113*x^9 + 96*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 74*x^3 + 32*x^2 + 89*x + 32, x^29 + 106*x^27 + 115*x^25 + 32*x^24 + 100*x^23 + 57*x^21 + 64*x^20 + 22*x^19 + 67*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 17*x^9 + 96*x^8 + 100*x^7 + 43*x^5 + 64*x^4 + 74*x^3 + 57*x + 32, x^29 + 106*x^27 + 80*x^26 + 83*x^25 + 16*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 112*x^18 + 99*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 49*x^9 + 112*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 16*x^2 + 25*x + 80, x^29 + 106*x^27 + 20*x^26 + 91*x^25 + 36*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 60*x^18 + 91*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 41*x^9 + 124*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 100*x^2 + 33*x + 84, x^29 + 106*x^27 + 108*x^26 + 11*x^25 + 44*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 68*x^18 + 43*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 121*x^9 + 52*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 28*x^2 + 81*x + 60, x^29 + 106*x^27 + 72*x^26 + 3*x^25 + 88*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 88*x^18 + 115*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + x^9 + 104*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 104*x^2 + 9*x + 120, x^29 + 106*x^27 + 112*x^26 + 99*x^25 + 96*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 80*x^18 + 83*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 33*x^9 + 32*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 48*x^2 + 41*x + 96, x^29 + 106*x^27 + 52*x^26 + 123*x^25 + 4*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 92*x^18 + 123*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 9*x^9 + 28*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 68*x^2 + x + 116, x^29 + 106*x^27 + 48*x^26 + 19*x^25 + 16*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 16*x^18 + 35*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 113*x^9 + 112*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 112*x^2 + 89*x + 80, x^29 + 106*x^27 + 124*x^26 + 27*x^25 + 12*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 116*x^18 + 27*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 105*x^9 + 84*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 108*x^2 + 97*x + 28, x^29 + 106*x^27 + 120*x^26 + 19*x^25 + 24*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 104*x^18 + 99*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 113*x^9 + 40*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 88*x^2 + 25*x + 56, x^29 + 106*x^27 + 19*x^25 + 64*x^24 + 100*x^23 + 121*x^21 + 22*x^19 + 35*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 113*x^9 + 64*x^8 + 100*x^7 + 107*x^5 + 74*x^3 + 89*x + 64, x^29 + 106*x^27 + 76*x^26 + 27*x^25 + 124*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 100*x^18 + 27*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 105*x^9 + 100*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 124*x^2 + 97*x + 76, x^29 + 106*x^27 + 4*x^26 + 123*x^25 + 52*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 12*x^18 + 59*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 9*x^9 + 108*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 20*x^2 + 65*x + 36, x^29 + 106*x^27 + 76*x^26 + 59*x^25 + 60*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 100*x^18 + 123*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 73*x^9 + 36*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 124*x^2 + x + 12, x^29 + 106*x^27 + 96*x^26 + 99*x^25 + 16*x^24 + 100*x^23 + 89*x^21 + 32*x^20 + 22*x^19 + 96*x^18 + 19*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 33*x^9 + 112*x^8 + 100*x^7 + 75*x^5 + 32*x^4 + 74*x^3 + 32*x^2 + 105*x + 16, x^29 + 106*x^27 + 76*x^26 + 75*x^25 + 76*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 100*x^18 + 107*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 57*x^9 + 20*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 124*x^2 + 17*x + 92, x^29 + 106*x^27 + 92*x^26 + 59*x^25 + 12*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 20*x^18 + 123*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 73*x^9 + 84*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 76*x^2 + x + 28, x^29 + 106*x^27 + 76*x^26 + 59*x^25 + 60*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 36*x^18 + 59*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 73*x^9 + 36*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 60*x^2 + 65*x + 76, x^29 + 106*x^27 + 44*x^26 + 123*x^25 + 92*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 4*x^18 + 59*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 9*x^9 + 4*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 92*x^2 + 65*x + 44, x^29 + 106*x^27 + 36*x^26 + 11*x^25 + 36*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 44*x^18 + 107*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 121*x^9 + 124*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 116*x^2 + 17*x + 20, x^29 + 106*x^27 + 84*x^26 + 11*x^25 + 52*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 60*x^18 + 107*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 121*x^9 + 108*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 100*x^2 + 17*x + 100, x^29 + 106*x^27 + 12*x^26 + 27*x^25 + 60*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 36*x^18 + 27*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 105*x^9 + 36*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 60*x^2 + 97*x + 12, x^29 + 106*x^27 + 84*x^26 + 43*x^25 + 116*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 60*x^18 + 75*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 89*x^9 + 44*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 100*x^2 + 49*x + 36, x^29 + 106*x^27 + 99*x^25 + 16*x^24 + 36*x^23 + 25*x^21 + 96*x^20 + 86*x^19 + 83*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 33*x^9 + 112*x^8 + 36*x^7 + 11*x^5 + 96*x^4 + 10*x^3 + 41*x + 80, x^29 + 106*x^27 + 12*x^26 + 123*x^25 + 92*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 100*x^18 + 123*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 9*x^9 + 4*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 124*x^2 + x + 108, x^29 + 106*x^27 + 76*x^26 + 43*x^25 + 12*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 36*x^18 + 75*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 89*x^9 + 84*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 60*x^2 + 49*x + 92, x^29 + 106*x^27 + 24*x^26 + 35*x^25 + 104*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 72*x^18 + 83*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 97*x^9 + 88*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 120*x^2 + 41*x + 72, x^29 + 106*x^27 + 40*x^26 + 67*x^25 + 88*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 120*x^18 + 51*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 65*x^9 + 104*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 72*x^2 + 73*x + 120, x^29 + 106*x^27 + 60*x^26 + 11*x^25 + 92*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 52*x^18 + 43*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 121*x^9 + 4*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 44*x^2 + 81*x + 44, x^29 + 106*x^27 + 16*x^26 + 67*x^25 + 64*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 112*x^18 + 51*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 65*x^9 + 64*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 16*x^2 + 73*x, x^29 + 106*x^27 + 36*x^26 + 75*x^25 + 68*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 108*x^18 + 107*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 57*x^9 + 92*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 52*x^2 + 17*x + 116, x^29 + 106*x^27 + 112*x^26 + 19*x^25 + 48*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 16*x^18 + 99*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 113*x^9 + 80*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 112*x^2 + 25*x + 48, x^29 + 106*x^27 + 96*x^26 + 67*x^25 + 16*x^24 + 100*x^23 + 25*x^21 + 32*x^20 + 22*x^19 + 96*x^18 + 51*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 65*x^9 + 112*x^8 + 100*x^7 + 11*x^5 + 32*x^4 + 74*x^3 + 32*x^2 + 73*x + 16, x^29 + 106*x^27 + 76*x^26 + 11*x^25 + 44*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 100*x^18 + 43*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 121*x^9 + 52*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 124*x^2 + 81*x + 60, x^29 + 106*x^27 + 112*x^26 + 67*x^25 + 96*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 80*x^18 + 115*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 65*x^9 + 32*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 48*x^2 + 9*x + 96, x^29 + 106*x^27 + 16*x^26 + 19*x^25 + 112*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 112*x^18 + 99*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 113*x^9 + 16*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 16*x^2 + 25*x + 112, x^29 + 106*x^27 + 80*x^26 + 51*x^25 + 112*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 112*x^18 + 3*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 81*x^9 + 16*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 16*x^2 + 121*x + 48, x^29 + 106*x^27 + 108*x^26 + 11*x^25 + 108*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 68*x^18 + 43*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 121*x^9 + 116*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 28*x^2 + 81*x + 124, x^29 + 106*x^27 + 40*x^26 + 19*x^25 + 72*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 120*x^18 + 99*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 113*x^9 + 120*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 72*x^2 + 25*x + 40, x^29 + 106*x^27 + 16*x^26 + 35*x^25 + 96*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 22*x^19 + 112*x^18 + 83*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 97*x^9 + 32*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 74*x^3 + 16*x^2 + 41*x + 32, x^29 + 106*x^27 + 84*x^26 + 107*x^25 + 20*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 124*x^18 + 75*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 25*x^9 + 12*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 36*x^2 + 49*x + 4, x^29 + 106*x^27 + 116*x^26 + 107*x^25 + 84*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 92*x^18 + 75*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 25*x^9 + 76*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 68*x^2 + 49*x + 68, x^29 + 106*x^27 + 84*x^26 + 27*x^25 + 68*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 124*x^18 + 27*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 105*x^9 + 92*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 36*x^2 + 97*x + 116, x^29 + 106*x^27 + 120*x^26 + 51*x^25 + 120*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 104*x^18 + 67*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 81*x^9 + 72*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 88*x^2 + 57*x + 24, x^29 + 106*x^27 + 40*x^26 + 115*x^25 + 104*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 120*x^18 + 3*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 17*x^9 + 88*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 72*x^2 + 121*x + 72, x^29 + 106*x^27 + 88*x^26 + 19*x^25 + 120*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 8*x^18 + 99*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 113*x^9 + 72*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 56*x^2 + 25*x + 24, x^29 + 106*x^27 + 120*x^26 + 67*x^25 + 104*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 40*x^18 + 115*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 65*x^9 + 88*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 24*x^2 + 9*x + 8, x^29 + 106*x^27 + 108*x^26 + 11*x^25 + 108*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 4*x^18 + 107*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 121*x^9 + 116*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 92*x^2 + 17*x + 60, x^29 + 106*x^27 + 40*x^26 + 99*x^25 + 56*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 56*x^18 + 83*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 33*x^9 + 8*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 8*x^2 + 41*x + 24, x^29 + 106*x^27 + 80*x^26 + 99*x^25 + 36*x^23 + 96*x^22 + 25*x^21 + 86*x^19 + 112*x^18 + 83*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 33*x^9 + 36*x^7 + 96*x^6 + 11*x^5 + 10*x^3 + 16*x^2 + 41*x, x^29 + 106*x^27 + 20*x^26 + 27*x^25 + 36*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 60*x^18 + 27*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 105*x^9 + 124*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 100*x^2 + 97*x + 84, x^29 + 106*x^27 + 112*x^26 + 3*x^25 + 64*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 16*x^18 + 115*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + x^9 + 64*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 112*x^2 + 9*x, x^29 + 106*x^27 + 92*x^26 + 43*x^25 + 92*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 84*x^18 + 75*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 89*x^9 + 4*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 12*x^2 + 49*x + 108, x^29 + 106*x^27 + 80*x^26 + 67*x^25 + 32*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 22*x^19 + 48*x^18 + 51*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 65*x^9 + 96*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 74*x^3 + 80*x^2 + 73*x + 96, x^29 + 106*x^27 + 4*x^26 + 91*x^25 + 116*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 12*x^18 + 91*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 41*x^9 + 44*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 20*x^2 + 33*x + 100, x^29 + 106*x^27 + 4*x^26 + 91*x^25 + 52*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 76*x^18 + 27*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 41*x^9 + 108*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 84*x^2 + 97*x + 100, x^29 + 106*x^27 + 124*x^26 + 27*x^25 + 108*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 52*x^18 + 91*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 105*x^9 + 116*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 44*x^2 + 33*x + 60, x^29 + 106*x^27 + 83*x^25 + 64*x^24 + 100*x^23 + 121*x^21 + 22*x^19 + 99*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 49*x^9 + 64*x^8 + 100*x^7 + 107*x^5 + 74*x^3 + 25*x + 64, x^29 + 106*x^27 + 40*x^26 + 3*x^25 + 56*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 120*x^18 + 115*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + x^9 + 8*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 72*x^2 + 9*x + 88, x^29 + 106*x^27 + 68*x^26 + 11*x^25 + 68*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 12*x^18 + 107*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 121*x^9 + 92*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 20*x^2 + 17*x + 52, x^29 + 106*x^27 + 72*x^26 + 35*x^25 + 24*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 24*x^18 + 19*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 97*x^9 + 40*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 40*x^2 + 105*x + 120, x^29 + 106*x^27 + 24*x^26 + 51*x^25 + 56*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 72*x^18 + 67*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 81*x^9 + 8*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 120*x^2 + 57*x + 88, x^29 + 106*x^27 + 84*x^26 + 27*x^25 + 4*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 60*x^18 + 91*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 105*x^9 + 28*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 100*x^2 + 33*x + 116, x^29 + 106*x^27 + 124*x^26 + 107*x^25 + 60*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 52*x^18 + 11*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 25*x^9 + 36*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 44*x^2 + 113*x + 76, x^29 + 106*x^27 + 100*x^26 + 59*x^25 + 84*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 108*x^18 + 59*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 73*x^9 + 76*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 52*x^2 + 65*x + 4, x^29 + 106*x^27 + 36*x^26 + 27*x^25 + 84*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 44*x^18 + 91*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 105*x^9 + 76*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 116*x^2 + 33*x + 4, x^29 + 106*x^27 + 60*x^26 + 107*x^25 + 28*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 52*x^18 + 75*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 25*x^9 + 68*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 44*x^2 + 49*x + 108, x^29 + 106*x^27 + 84*x^26 + 75*x^25 + 84*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 60*x^18 + 43*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 57*x^9 + 76*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 100*x^2 + 81*x + 4, x^29 + 106*x^27 + 40*x^26 + 19*x^25 + 40*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 120*x^18 + 99*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 113*x^9 + 24*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 72*x^2 + 25*x + 8, x^29 + 106*x^27 + 28*x^26 + 59*x^25 + 76*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 20*x^18 + 59*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 73*x^9 + 20*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 76*x^2 + 65*x + 28, x^29 + 106*x^27 + 100*x^26 + 75*x^25 + 68*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 108*x^18 + 43*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 57*x^9 + 92*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 52*x^2 + 81*x + 52, x^29 + 106*x^27 + 56*x^26 + 35*x^25 + 8*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 104*x^18 + 19*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 97*x^9 + 56*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 88*x^2 + 105*x + 40, x^29 + 106*x^27 + 16*x^26 + 83*x^25 + 16*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 112*x^18 + 35*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 49*x^9 + 112*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 16*x^2 + 89*x + 16, x^29 + 106*x^27 + 28*x^26 + 27*x^25 + 76*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 84*x^18 + 27*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 105*x^9 + 20*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 12*x^2 + 97*x + 92, x^29 + 106*x^27 + 72*x^26 + 83*x^25 + 72*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 24*x^18 + 99*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 49*x^9 + 120*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 40*x^2 + 25*x + 104, x^29 + 106*x^27 + 120*x^26 + 51*x^25 + 24*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 40*x^18 + 3*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 81*x^9 + 40*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 24*x^2 + 121*x + 120, x^29 + 106*x^27 + 112*x^26 + 115*x^25 + 112*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 80*x^18 + 67*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 17*x^9 + 16*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 48*x^2 + 57*x + 48, x^29 + 106*x^27 + 88*x^26 + 3*x^25 + 8*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 8*x^18 + 115*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + x^9 + 56*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 56*x^2 + 9*x + 104, x^29 + 106*x^27 + 68*x^26 + 75*x^25 + 36*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 76*x^18 + 107*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 57*x^9 + 124*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 84*x^2 + 17*x + 84, x^29 + 106*x^27 + 16*x^26 + 3*x^25 + 64*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 86*x^19 + 48*x^18 + 51*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + x^9 + 64*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 10*x^3 + 80*x^2 + 73*x + 64, x^29 + 106*x^27 + 116*x^26 + 11*x^25 + 20*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 28*x^18 + 107*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 121*x^9 + 12*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 4*x^2 + 17*x + 68, x^29 + 106*x^27 + 64*x^26 + 83*x^25 + 36*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 86*x^19 + 35*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 49*x^9 + 36*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 10*x^3 + 89*x + 64, x^29 + 106*x^27 + 36*x^26 + 43*x^25 + 68*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 44*x^18 + 75*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 89*x^9 + 92*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 116*x^2 + 49*x + 52, x^29 + 106*x^27 + 116*x^26 + 59*x^25 + 68*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 28*x^18 + 59*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 73*x^9 + 92*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 4*x^2 + 65*x + 52, x^29 + 106*x^27 + 36*x^26 + 11*x^25 + 4*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 44*x^18 + 107*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 121*x^9 + 28*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 116*x^2 + 17*x + 116, x^29 + 106*x^27 + 84*x^26 + 91*x^25 + 100*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 124*x^18 + 91*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 41*x^9 + 60*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 36*x^2 + 33*x + 20, x^29 + 106*x^27 + 44*x^26 + 43*x^25 + 12*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 4*x^18 + 11*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 89*x^9 + 84*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 92*x^2 + 113*x + 28, x^29 + 106*x^27 + 16*x^26 + 83*x^25 + 48*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 112*x^18 + 35*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 49*x^9 + 80*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 16*x^2 + 89*x + 48, x^29 + 106*x^27 + 68*x^26 + 43*x^25 + 36*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 12*x^18 + 75*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 89*x^9 + 124*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 20*x^2 + 49*x + 20, x^29 + 106*x^27 + 16*x^26 + 67*x^25 + 36*x^23 + 96*x^22 + 89*x^21 + 86*x^19 + 48*x^18 + 115*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 65*x^9 + 36*x^7 + 96*x^6 + 75*x^5 + 10*x^3 + 80*x^2 + 9*x, x^29 + 106*x^27 + 20*x^26 + 123*x^25 + 68*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 124*x^18 + 123*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 9*x^9 + 92*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 36*x^2 + x + 52, x^29 + 106*x^27 + 92*x^26 + 123*x^25 + 76*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 20*x^18 + 59*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 9*x^9 + 20*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 76*x^2 + 65*x + 92, x^29 + 106*x^27 + 96*x^26 + 3*x^25 + 80*x^24 + 100*x^23 + 25*x^21 + 32*x^20 + 22*x^19 + 96*x^18 + 115*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + x^9 + 48*x^8 + 100*x^7 + 11*x^5 + 32*x^4 + 74*x^3 + 32*x^2 + 9*x + 80, x^29 + 106*x^27 + 115*x^25 + 64*x^24 + 100*x^23 + 57*x^21 + 22*x^19 + 67*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 17*x^9 + 64*x^8 + 100*x^7 + 43*x^5 + 74*x^3 + 57*x + 64, x^29 + 106*x^27 + 68*x^26 + 123*x^25 + 84*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 12*x^18 + 123*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 9*x^9 + 76*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 20*x^2 + x + 4, x^29 + 106*x^27 + 48*x^26 + 99*x^25 + 96*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 16*x^18 + 83*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 33*x^9 + 32*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 112*x^2 + 41*x + 96, x^29 + 106*x^27 + 100*x^26 + 27*x^25 + 52*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 44*x^18 + 27*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 105*x^9 + 108*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 116*x^2 + 97*x + 36, x^29 + 106*x^27 + 72*x^26 + 83*x^25 + 104*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 88*x^18 + 35*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 49*x^9 + 88*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 104*x^2 + 89*x + 72, x^29 + 106*x^27 + 28*x^26 + 43*x^25 + 28*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 20*x^18 + 75*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 89*x^9 + 68*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 76*x^2 + 49*x + 44, x^29 + 106*x^27 + 100*x^26 + 91*x^25 + 52*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 44*x^18 + 91*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 41*x^9 + 108*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 116*x^2 + 33*x + 36, x^29 + 106*x^27 + 124*x^26 + 123*x^25 + 108*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 116*x^18 + 59*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 9*x^9 + 116*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 108*x^2 + 65*x + 124, x^29 + 106*x^27 + 48*x^26 + 115*x^25 + 112*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 16*x^18 + 67*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 17*x^9 + 16*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 112*x^2 + 57*x + 48, x^29 + 106*x^27 + 116*x^26 + 91*x^25 + 100*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 92*x^18 + 91*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 41*x^9 + 60*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 68*x^2 + 33*x + 20, x^29 + 106*x^27 + 100*x^26 + 43*x^25 + 100*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 44*x^18 + 11*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 89*x^9 + 60*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 116*x^2 + 113*x + 20, x^29 + 106*x^27 + 44*x^26 + 75*x^25 + 108*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 68*x^18 + 43*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 57*x^9 + 116*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 28*x^2 + 81*x + 60, x^29 + 106*x^27 + 124*x^26 + 75*x^25 + 124*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 52*x^18 + 43*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 57*x^9 + 100*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 44*x^2 + 81*x + 12, x^29 + 106*x^27 + 48*x^26 + 99*x^25 + 32*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 22*x^19 + 80*x^18 + 19*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 33*x^9 + 96*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 74*x^3 + 48*x^2 + 105*x + 96, x^29 + 106*x^27 + 104*x^26 + 99*x^25 + 88*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 56*x^18 + 19*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 33*x^9 + 104*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 8*x^2 + 105*x + 120, x^29 + 106*x^27 + 44*x^26 + 107*x^25 + 44*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 4*x^18 + 75*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 25*x^9 + 52*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 92*x^2 + 49*x + 60, x^29 + 106*x^27 + 104*x^26 + 35*x^25 + 56*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 120*x^18 + 19*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 97*x^9 + 8*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 72*x^2 + 105*x + 24, x^29 + 106*x^27 + 8*x^26 + 67*x^25 + 24*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 88*x^18 + 115*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 65*x^9 + 40*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 104*x^2 + 9*x + 120, x^29 + 106*x^27 + 32*x^26 + 3*x^25 + 16*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 86*x^19 + 96*x^18 + 51*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + x^9 + 112*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 10*x^3 + 32*x^2 + 73*x + 80, x^29 + 106*x^27 + 56*x^26 + 99*x^25 + 104*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 104*x^18 + 83*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 33*x^9 + 88*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 88*x^2 + 41*x + 8, x^29 + 106*x^27 + 96*x^26 + 99*x^25 + 80*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 86*x^19 + 32*x^18 + 83*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 33*x^9 + 48*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 10*x^3 + 96*x^2 + 41*x + 16, x^29 + 106*x^27 + 96*x^26 + 67*x^25 + 112*x^24 + 100*x^23 + 25*x^21 + 96*x^20 + 22*x^19 + 96*x^18 + 51*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 65*x^9 + 16*x^8 + 100*x^7 + 11*x^5 + 96*x^4 + 74*x^3 + 32*x^2 + 73*x + 112, x^29 + 106*x^27 + 80*x^26 + 83*x^25 + 48*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 48*x^18 + 35*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 49*x^9 + 80*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 80*x^2 + 89*x + 48, x^29 + 106*x^27 + 72*x^26 + 35*x^25 + 88*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 88*x^18 + 83*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 97*x^9 + 104*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 104*x^2 + 41*x + 120, x^29 + 106*x^27 + 108*x^26 + 123*x^25 + 124*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 68*x^18 + 59*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 9*x^9 + 100*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 28*x^2 + 65*x + 76, x^29 + 106*x^27 + 84*x^26 + 75*x^25 + 116*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 60*x^18 + 43*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 57*x^9 + 44*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 100*x^2 + 81*x + 36, x^29 + 106*x^27 + 16*x^26 + 19*x^25 + 112*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 48*x^18 + 35*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 113*x^9 + 16*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 80*x^2 + 89*x + 48, x^29 + 106*x^27 + 124*x^26 + 43*x^25 + 28*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 52*x^18 + 75*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 89*x^9 + 68*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 44*x^2 + 49*x + 44, x^29 + 106*x^27 + 104*x^26 + 19*x^25 + 104*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 120*x^18 + 35*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 113*x^9 + 88*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 72*x^2 + 89*x + 8, x^29 + 106*x^27 + 112*x^26 + 51*x^25 + 16*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 80*x^18 + 3*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 81*x^9 + 112*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 48*x^2 + 121*x + 80, x^29 + 106*x^27 + 76*x^26 + 27*x^25 + 92*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 36*x^18 + 91*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 105*x^9 + 4*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 60*x^2 + 33*x + 108, x^29 + 106*x^27 + 56*x^26 + 35*x^25 + 104*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 104*x^18 + 19*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 97*x^9 + 88*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 88*x^2 + 105*x + 8, x^29 + 106*x^27 + 112*x^26 + 35*x^25 + 100*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 16*x^18 + 83*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 97*x^9 + 100*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 112*x^2 + 41*x + 64, x^29 + 106*x^27 + 36*x^26 + 27*x^25 + 52*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 108*x^18 + 27*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 105*x^9 + 108*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 52*x^2 + 97*x + 36, x^29 + 106*x^27 + 8*x^26 + 99*x^25 + 24*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 88*x^18 + 83*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 33*x^9 + 40*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 104*x^2 + 41*x + 120, x^29 + 106*x^27 + 56*x^26 + 35*x^25 + 8*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 40*x^18 + 83*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 97*x^9 + 56*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 24*x^2 + 41*x + 104, x^29 + 106*x^27 + 120*x^26 + 115*x^25 + 24*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 40*x^18 + 67*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 17*x^9 + 40*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 24*x^2 + 57*x + 120, x^29 + 106*x^27 + 116*x^26 + 59*x^25 + 4*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 92*x^18 + 123*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 73*x^9 + 28*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 68*x^2 + x + 52, x^29 + 106*x^27 + 56*x^26 + 51*x^25 + 24*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 40*x^18 + 67*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 81*x^9 + 40*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 24*x^2 + 57*x + 56, x^29 + 106*x^27 + 67*x^25 + 16*x^24 + 36*x^23 + 89*x^21 + 96*x^20 + 86*x^19 + 115*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 65*x^9 + 112*x^8 + 36*x^7 + 75*x^5 + 96*x^4 + 10*x^3 + 9*x + 80, x^29 + 106*x^27 + 12*x^26 + 91*x^25 + 28*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 36*x^18 + 91*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 41*x^9 + 68*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 60*x^2 + 33*x + 108, x^29 + 106*x^27 + 8*x^26 + 19*x^25 + 8*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 24*x^18 + 99*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 113*x^9 + 56*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 40*x^2 + 25*x + 104, x^29 + 106*x^27 + 72*x^26 + 99*x^25 + 56*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 88*x^18 + 19*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 33*x^9 + 8*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 104*x^2 + 105*x + 88, x^29 + 106*x^27 + 116*x^26 + 11*x^25 + 52*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 28*x^18 + 107*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 121*x^9 + 108*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 4*x^2 + 17*x + 100, x^29 + 106*x^27 + 76*x^26 + 11*x^25 + 12*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 100*x^18 + 43*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 121*x^9 + 84*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 124*x^2 + 81*x + 28, x^29 + 106*x^27 + 24*x^26 + 19*x^25 + 120*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 72*x^18 + 99*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 113*x^9 + 72*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 120*x^2 + 25*x + 24, x^29 + 106*x^27 + 8*x^26 + 67*x^25 + 24*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 24*x^18 + 51*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 65*x^9 + 40*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 40*x^2 + 73*x + 56, x^29 + 106*x^27 + 88*x^26 + 51*x^25 + 24*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 72*x^18 + 3*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 81*x^9 + 40*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 120*x^2 + 121*x + 120, x^29 + 106*x^27 + 68*x^26 + 123*x^25 + 116*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 12*x^18 + 123*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 9*x^9 + 44*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 20*x^2 + x + 36, x^29 + 106*x^27 + 100*x^26 + 107*x^25 + 68*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 44*x^18 + 75*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 25*x^9 + 92*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 116*x^2 + 49*x + 116, x^29 + 106*x^27 + 32*x^26 + 3*x^25 + 80*x^24 + 100*x^23 + 25*x^21 + 32*x^20 + 22*x^19 + 32*x^18 + 115*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + x^9 + 48*x^8 + 100*x^7 + 11*x^5 + 32*x^4 + 74*x^3 + 96*x^2 + 9*x + 80, x^29 + 106*x^27 + 68*x^26 + 11*x^25 + 68*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 76*x^18 + 43*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 121*x^9 + 92*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 84*x^2 + 81*x + 116, x^29 + 106*x^27 + 96*x^26 + 19*x^25 + 36*x^23 + 57*x^21 + 64*x^20 + 86*x^19 + 96*x^18 + 99*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 113*x^9 + 36*x^7 + 43*x^5 + 64*x^4 + 10*x^3 + 32*x^2 + 25*x + 64, x^29 + 106*x^27 + 120*x^26 + 3*x^25 + 104*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 40*x^18 + 51*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + x^9 + 88*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 24*x^2 + 73*x + 8, x^29 + 106*x^27 + 56*x^26 + 35*x^25 + 40*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 104*x^18 + 19*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 97*x^9 + 24*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 88*x^2 + 105*x + 72, x^29 + 106*x^27 + 120*x^26 + 19*x^25 + 24*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 40*x^18 + 35*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 113*x^9 + 40*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 24*x^2 + 89*x + 120, x^29 + 106*x^27 + 48*x^26 + 115*x^25 + 80*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 80*x^18 + 3*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 17*x^9 + 48*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 48*x^2 + 121*x + 80, x^29 + 106*x^27 + 44*x^26 + 91*x^25 + 124*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 4*x^18 + 91*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 41*x^9 + 100*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 92*x^2 + 33*x + 76, x^29 + 106*x^27 + 28*x^26 + 123*x^25 + 76*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 20*x^18 + 123*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 9*x^9 + 20*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 76*x^2 + x + 28, x^29 + 106*x^27 + 52*x^26 + 91*x^25 + 100*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 28*x^18 + 91*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 41*x^9 + 60*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 4*x^2 + 33*x + 20, x^29 + 106*x^27 + 120*x^26 + 19*x^25 + 56*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 104*x^18 + 99*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 113*x^9 + 8*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 88*x^2 + 25*x + 88, x^29 + 106*x^27 + 48*x^26 + 83*x^25 + 48*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 16*x^18 + 99*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 49*x^9 + 80*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 112*x^2 + 25*x + 112, x^29 + 106*x^27 + 68*x^26 + 59*x^25 + 116*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 12*x^18 + 59*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 73*x^9 + 44*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 20*x^2 + 65*x + 36, x^29 + 106*x^27 + 96*x^26 + 67*x^25 + 16*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 86*x^19 + 32*x^18 + 115*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 65*x^9 + 112*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 10*x^3 + 96*x^2 + 9*x + 80, x^29 + 106*x^27 + 60*x^26 + 43*x^25 + 60*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 116*x^18 + 75*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 89*x^9 + 36*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 108*x^2 + 49*x + 76, x^29 + 106*x^27 + 40*x^26 + 51*x^25 + 104*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 120*x^18 + 67*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 81*x^9 + 88*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 72*x^2 + 57*x + 72, x^29 + 106*x^27 + 68*x^26 + 59*x^25 + 52*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 12*x^18 + 59*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 73*x^9 + 108*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 20*x^2 + 65*x + 100, x^29 + 106*x^27 + 40*x^26 + 83*x^25 + 72*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 120*x^18 + 35*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 49*x^9 + 120*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 72*x^2 + 89*x + 40, x^29 + 106*x^27 + 24*x^26 + 115*x^25 + 88*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 8*x^18 + 67*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 17*x^9 + 104*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 56*x^2 + 57*x + 56, x^29 + 106*x^27 + 112*x^26 + 83*x^25 + 16*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 80*x^18 + 99*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 49*x^9 + 112*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 48*x^2 + 25*x + 80, x^29 + 106*x^27 + 32*x^26 + 19*x^25 + 100*x^23 + 64*x^22 + 121*x^21 + 22*x^19 + 96*x^18 + 35*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 113*x^9 + 100*x^7 + 64*x^6 + 107*x^5 + 74*x^3 + 32*x^2 + 89*x, x^29 + 106*x^27 + 67*x^25 + 48*x^24 + 36*x^23 + 89*x^21 + 32*x^20 + 86*x^19 + 115*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 65*x^9 + 80*x^8 + 36*x^7 + 75*x^5 + 32*x^4 + 10*x^3 + 9*x + 112, x^29 + 106*x^27 + 60*x^26 + 27*x^25 + 44*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 116*x^18 + 91*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 105*x^9 + 52*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 108*x^2 + 33*x + 124, x^29 + 106*x^27 + 60*x^26 + 123*x^25 + 108*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 116*x^18 + 123*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 9*x^9 + 116*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 108*x^2 + x + 60, x^29 + 106*x^27 + 44*x^26 + 75*x^25 + 12*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 68*x^18 + 43*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 57*x^9 + 84*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 28*x^2 + 81*x + 92, x^29 + 106*x^27 + 60*x^26 + 59*x^25 + 76*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 52*x^18 + 123*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 73*x^9 + 20*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 44*x^2 + x + 92, x^29 + 106*x^27 + 116*x^26 + 43*x^25 + 20*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 28*x^18 + 75*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 89*x^9 + 12*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 4*x^2 + 49*x + 68, x^29 + 106*x^27 + 80*x^26 + 3*x^25 + 64*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 86*x^19 + 112*x^18 + 51*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + x^9 + 64*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 10*x^3 + 16*x^2 + 73*x + 64, x^29 + 106*x^27 + 92*x^26 + 27*x^25 + 76*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 84*x^18 + 91*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 105*x^9 + 20*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 12*x^2 + 33*x + 28, x^29 + 106*x^27 + 76*x^26 + 91*x^25 + 92*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 36*x^18 + 27*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 41*x^9 + 4*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 60*x^2 + 97*x + 108, x^29 + 106*x^27 + 4*x^26 + 75*x^25 + 36*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 12*x^18 + 107*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 57*x^9 + 124*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 20*x^2 + 17*x + 84, x^29 + 106*x^27 + 100*x^26 + 107*x^25 + 4*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 108*x^18 + 11*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 25*x^9 + 28*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 52*x^2 + 113*x + 116, x^29 + 106*x^27 + 28*x^26 + 27*x^25 + 108*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 20*x^18 + 91*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 105*x^9 + 116*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 76*x^2 + 33*x + 60, x^29 + 106*x^27 + 28*x^26 + 75*x^25 + 124*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 84*x^18 + 107*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 57*x^9 + 100*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 12*x^2 + 17*x + 76, x^29 + 106*x^27 + 24*x^26 + 99*x^25 + 40*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 72*x^18 + 19*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 33*x^9 + 24*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 120*x^2 + 105*x + 8, x^29 + 106*x^27 + 60*x^26 + 11*x^25 + 92*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 116*x^18 + 107*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 121*x^9 + 4*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 108*x^2 + 17*x + 108, x^29 + 106*x^27 + 92*x^26 + 27*x^25 + 108*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 20*x^18 + 27*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 105*x^9 + 116*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 76*x^2 + 97*x + 124, x^29 + 106*x^27 + 84*x^26 + 75*x^25 + 52*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 60*x^18 + 43*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 57*x^9 + 108*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 100*x^2 + 81*x + 100, x^29 + 106*x^27 + 32*x^26 + 99*x^25 + 80*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 86*x^19 + 96*x^18 + 83*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 33*x^9 + 48*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 10*x^3 + 32*x^2 + 41*x + 16, x^29 + 106*x^27 + 48*x^26 + 67*x^25 + 96*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 22*x^19 + 80*x^18 + 51*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 65*x^9 + 32*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 74*x^3 + 48*x^2 + 73*x + 32, x^29 + 106*x^27 + 52*x^26 + 11*x^25 + 84*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 92*x^18 + 107*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 121*x^9 + 76*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 68*x^2 + 17*x + 4, x^29 + 106*x^27 + 32*x^26 + 19*x^25 + 64*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 22*x^19 + 96*x^18 + 35*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 113*x^9 + 64*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 74*x^3 + 32*x^2 + 89*x + 64, x^29 + 106*x^27 + 20*x^26 + 59*x^25 + 68*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 60*x^18 + 123*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 73*x^9 + 92*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 100*x^2 + x + 116, x^29 + 106*x^27 + 80*x^26 + 99*x^25 + 100*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 48*x^18 + 19*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 33*x^9 + 100*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 80*x^2 + 105*x + 64, x^29 + 106*x^27 + 104*x^26 + 83*x^25 + 8*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 56*x^18 + 35*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 49*x^9 + 56*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 8*x^2 + 89*x + 104, x^29 + 106*x^27 + 40*x^26 + 99*x^25 + 24*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 56*x^18 + 83*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 33*x^9 + 40*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 8*x^2 + 41*x + 120, x^29 + 106*x^27 + 120*x^26 + 83*x^25 + 56*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 40*x^18 + 99*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 49*x^9 + 8*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 24*x^2 + 25*x + 24, x^29 + 106*x^27 + 72*x^26 + 115*x^25 + 8*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 24*x^18 + 67*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 17*x^9 + 56*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 40*x^2 + 57*x + 40, x^29 + 106*x^27 + 80*x^26 + 67*x^25 + 36*x^23 + 96*x^22 + 89*x^21 + 86*x^19 + 112*x^18 + 115*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 65*x^9 + 36*x^7 + 96*x^6 + 75*x^5 + 10*x^3 + 16*x^2 + 9*x, x^29 + 106*x^27 + 28*x^26 + 43*x^25 + 60*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 20*x^18 + 75*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 89*x^9 + 36*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 76*x^2 + 49*x + 76, x^29 + 106*x^27 + 120*x^26 + 83*x^25 + 88*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 104*x^18 + 35*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 49*x^9 + 104*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 88*x^2 + 89*x + 120, x^29 + 106*x^27 + 32*x^26 + 67*x^25 + 80*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 86*x^19 + 96*x^18 + 115*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 65*x^9 + 48*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 10*x^3 + 32*x^2 + 9*x + 16, x^29 + 106*x^27 + 56*x^26 + 99*x^25 + 104*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 40*x^18 + 19*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 33*x^9 + 88*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 24*x^2 + 105*x + 72, x^29 + 106*x^27 + 104*x^26 + 115*x^25 + 72*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 120*x^18 + 67*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 17*x^9 + 120*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 72*x^2 + 57*x + 104, x^29 + 106*x^27 + 96*x^26 + 3*x^25 + 48*x^24 + 100*x^23 + 25*x^21 + 96*x^20 + 22*x^19 + 96*x^18 + 115*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + x^9 + 80*x^8 + 100*x^7 + 11*x^5 + 96*x^4 + 74*x^3 + 32*x^2 + 9*x + 48, x^29 + 106*x^27 + 28*x^26 + 27*x^25 + 76*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 20*x^18 + 91*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 105*x^9 + 20*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 76*x^2 + 33*x + 28, x^29 + 106*x^27 + 12*x^26 + 75*x^25 + 76*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 100*x^18 + 43*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 57*x^9 + 20*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 124*x^2 + 81*x + 28, x^29 + 106*x^27 + 88*x^26 + 3*x^25 + 72*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 8*x^18 + 115*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + x^9 + 120*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 56*x^2 + 9*x + 40, x^29 + 106*x^27 + 76*x^26 + 43*x^25 + 44*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 36*x^18 + 75*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 89*x^9 + 52*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 60*x^2 + 49*x + 124, x^29 + 106*x^27 + 96*x^26 + 115*x^25 + 32*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 22*x^19 + 32*x^18 + 67*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 17*x^9 + 96*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 74*x^3 + 96*x^2 + 57*x + 32, x^29 + 106*x^27 + 8*x^26 + 35*x^25 + 120*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 24*x^18 + 83*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 97*x^9 + 72*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 40*x^2 + 41*x + 24, x^29 + 106*x^27 + 28*x^26 + 107*x^25 + 92*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 84*x^18 + 75*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 25*x^9 + 4*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 12*x^2 + 49*x + 44, x^29 + 106*x^27 + 48*x^26 + 19*x^25 + 112*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 16*x^18 + 35*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 113*x^9 + 16*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 112*x^2 + 89*x + 48, x^29 + 106*x^27 + 67*x^25 + 112*x^24 + 36*x^23 + 89*x^21 + 32*x^20 + 86*x^19 + 115*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 65*x^9 + 16*x^8 + 36*x^7 + 75*x^5 + 32*x^4 + 10*x^3 + 9*x + 48, x^29 + 106*x^27 + 16*x^26 + 51*x^25 + 112*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 112*x^18 + 67*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 81*x^9 + 16*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 16*x^2 + 57*x + 112, x^29 + 106*x^27 + 76*x^26 + 11*x^25 + 76*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 100*x^18 + 43*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 121*x^9 + 20*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 124*x^2 + 81*x + 92, x^29 + 106*x^27 + 48*x^26 + 67*x^25 + 32*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 22*x^19 + 80*x^18 + 51*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 65*x^9 + 96*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 74*x^3 + 48*x^2 + 73*x + 96, x^29 + 106*x^27 + 60*x^26 + 27*x^25 + 108*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 52*x^18 + 27*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 105*x^9 + 116*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 44*x^2 + 97*x + 124, x^29 + 106*x^27 + 40*x^26 + 67*x^25 + 24*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 56*x^18 + 115*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 65*x^9 + 40*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 8*x^2 + 9*x + 120, x^29 + 106*x^27 + 108*x^26 + 123*x^25 + 28*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 4*x^18 + 123*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 9*x^9 + 68*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 92*x^2 + x + 44, x^29 + 106*x^27 + 8*x^26 + 3*x^25 + 24*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 88*x^18 + 51*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + x^9 + 40*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 104*x^2 + 73*x + 120, x^29 + 106*x^27 + 88*x^26 + 115*x^25 + 56*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 72*x^18 + 67*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 17*x^9 + 8*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 120*x^2 + 57*x + 24, x^29 + 106*x^27 + 116*x^26 + 91*x^25 + 68*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 28*x^18 + 27*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 41*x^9 + 92*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 4*x^2 + 97*x + 52, x^29 + 106*x^27 + 96*x^26 + 35*x^25 + 48*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 86*x^19 + 32*x^18 + 19*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 97*x^9 + 80*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 10*x^3 + 96*x^2 + 105*x + 112, x^29 + 106*x^27 + 124*x^26 + 43*x^25 + 92*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 52*x^18 + 75*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 89*x^9 + 4*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 44*x^2 + 49*x + 108, x^29 + 106*x^27 + 60*x^26 + 75*x^25 + 124*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 116*x^18 + 43*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 57*x^9 + 100*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 108*x^2 + 81*x + 12, x^29 + 106*x^27 + 96*x^26 + 51*x^25 + 32*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 22*x^19 + 32*x^18 + 3*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 81*x^9 + 96*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 74*x^3 + 96*x^2 + 121*x + 32, x^29 + 106*x^27 + 80*x^26 + 115*x^25 + 80*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 112*x^18 + 67*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 17*x^9 + 48*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 16*x^2 + 57*x + 16, x^29 + 106*x^27 + 92*x^26 + 91*x^25 + 108*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 84*x^18 + 27*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 41*x^9 + 116*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 12*x^2 + 97*x + 60, x^29 + 106*x^27 + 4*x^26 + 11*x^25 + 36*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 76*x^18 + 107*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 121*x^9 + 124*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 84*x^2 + 17*x + 20, x^29 + 106*x^27 + 24*x^26 + 83*x^25 + 88*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 72*x^18 + 35*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 49*x^9 + 104*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 120*x^2 + 89*x + 120, x^29 + 106*x^27 + 8*x^26 + 3*x^25 + 56*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 24*x^18 + 115*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + x^9 + 8*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 40*x^2 + 9*x + 88, x^29 + 106*x^27 + 28*x^26 + 75*x^25 + 60*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 20*x^18 + 43*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 57*x^9 + 36*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 76*x^2 + 81*x + 76, x^29 + 106*x^27 + 20*x^26 + 27*x^25 + 68*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 124*x^18 + 91*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 105*x^9 + 92*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 36*x^2 + 33*x + 52, x^29 + 106*x^27 + 83*x^25 + 96*x^24 + 100*x^23 + 121*x^21 + 64*x^20 + 22*x^19 + 99*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 49*x^9 + 32*x^8 + 100*x^7 + 107*x^5 + 64*x^4 + 74*x^3 + 25*x + 96, x^29 + 106*x^27 + 28*x^26 + 123*x^25 + 12*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 20*x^18 + 123*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 9*x^9 + 84*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 76*x^2 + x + 92, x^29 + 106*x^27 + 116*x^26 + 91*x^25 + 4*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 28*x^18 + 27*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 41*x^9 + 28*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 4*x^2 + 97*x + 116, x^29 + 106*x^27 + 76*x^26 + 27*x^25 + 60*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 100*x^18 + 27*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 105*x^9 + 36*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 124*x^2 + 97*x + 12, x^29 + 106*x^27 + 68*x^26 + 27*x^25 + 84*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 12*x^18 + 91*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 105*x^9 + 76*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 20*x^2 + 33*x + 4, x^29 + 106*x^27 + 88*x^26 + 3*x^25 + 40*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 8*x^18 + 115*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + x^9 + 24*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 56*x^2 + 9*x + 8, x^29 + 106*x^27 + 120*x^26 + 115*x^25 + 56*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 40*x^18 + 67*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 17*x^9 + 8*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 24*x^2 + 57*x + 24, x^29 + 106*x^27 + 112*x^26 + 19*x^25 + 80*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 16*x^18 + 99*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 113*x^9 + 48*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 112*x^2 + 25*x + 80, x^29 + 106*x^27 + 76*x^26 + 43*x^25 + 108*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 36*x^18 + 75*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 89*x^9 + 116*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 60*x^2 + 49*x + 60, x^29 + 106*x^27 + 56*x^26 + 51*x^25 + 56*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 104*x^18 + 3*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 81*x^9 + 8*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 88*x^2 + 121*x + 24, x^29 + 106*x^27 + 28*x^26 + 11*x^25 + 124*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 84*x^18 + 43*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 121*x^9 + 100*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 12*x^2 + 81*x + 76, x^29 + 106*x^27 + 124*x^26 + 11*x^25 + 92*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 116*x^18 + 43*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 121*x^9 + 4*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 108*x^2 + 81*x + 44, x^29 + 106*x^27 + 112*x^26 + 99*x^25 + 100*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 16*x^18 + 19*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 33*x^9 + 100*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 112*x^2 + 105*x + 64, x^29 + 106*x^27 + 16*x^26 + 115*x^25 + 80*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 48*x^18 + 67*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 17*x^9 + 48*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 80*x^2 + 57*x + 16, x^29 + 106*x^27 + 84*x^26 + 91*x^25 + 4*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 124*x^18 + 91*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 41*x^9 + 28*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 36*x^2 + 33*x + 52, x^29 + 106*x^27 + 44*x^26 + 123*x^25 + 60*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 4*x^18 + 59*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 9*x^9 + 36*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 92*x^2 + 65*x + 12, x^29 + 106*x^27 + 56*x^26 + 3*x^25 + 40*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 104*x^18 + 51*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + x^9 + 24*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 88*x^2 + 73*x + 72, x^29 + 106*x^27 + 80*x^26 + 3*x^25 + 64*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 48*x^18 + 115*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + x^9 + 64*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 80*x^2 + 9*x, x^29 + 106*x^27 + 84*x^26 + 123*x^25 + 68*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 124*x^18 + 59*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 9*x^9 + 92*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 36*x^2 + 65*x + 116, x^29 + 106*x^27 + 44*x^26 + 27*x^25 + 28*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 68*x^18 + 91*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 105*x^9 + 68*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 28*x^2 + 33*x + 44, x^29 + 106*x^27 + 40*x^26 + 3*x^25 + 88*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 56*x^18 + 51*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + x^9 + 104*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 8*x^2 + 73*x + 56, x^29 + 106*x^27 + 64*x^26 + 99*x^25 + 48*x^24 + 36*x^23 + 25*x^21 + 32*x^20 + 86*x^19 + 64*x^18 + 83*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 33*x^9 + 80*x^8 + 36*x^7 + 11*x^5 + 32*x^4 + 10*x^3 + 64*x^2 + 41*x + 112, x^29 + 106*x^27 + 92*x^26 + 123*x^25 + 108*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 20*x^18 + 59*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 9*x^9 + 116*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 76*x^2 + 65*x + 124, x^29 + 106*x^27 + 88*x^26 + 83*x^25 + 120*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 72*x^18 + 99*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 49*x^9 + 72*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 120*x^2 + 25*x + 88, x^29 + 106*x^27 + 112*x^26 + 83*x^25 + 48*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 16*x^18 + 35*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 49*x^9 + 80*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 112*x^2 + 89*x + 48, x^29 + 106*x^27 + 100*x^26 + 123*x^25 + 84*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 44*x^18 + 59*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 9*x^9 + 76*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 116*x^2 + 65*x + 68, x^29 + 106*x^27 + 40*x^26 + 99*x^25 + 56*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 120*x^18 + 19*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 33*x^9 + 8*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 72*x^2 + 105*x + 88, x^29 + 106*x^27 + 36*x^26 + 123*x^25 + 20*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 44*x^18 + 123*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 9*x^9 + 12*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 116*x^2 + x + 68, x^29 + 106*x^27 + 112*x^26 + 3*x^25 + 32*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 22*x^19 + 16*x^18 + 115*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + x^9 + 96*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 74*x^3 + 112*x^2 + 9*x + 96, x^29 + 106*x^27 + 80*x^26 + 99*x^25 + 96*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 22*x^19 + 48*x^18 + 19*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 33*x^9 + 32*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 74*x^3 + 80*x^2 + 105*x + 32, x^29 + 106*x^27 + 72*x^26 + 99*x^25 + 24*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 88*x^18 + 19*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 33*x^9 + 40*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 104*x^2 + 105*x + 56, x^29 + 106*x^27 + 88*x^26 + 51*x^25 + 88*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 8*x^18 + 67*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 81*x^9 + 104*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 56*x^2 + 57*x + 120, x^29 + 106*x^27 + 100*x^26 + 59*x^25 + 20*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 44*x^18 + 123*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 73*x^9 + 12*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 116*x^2 + x + 4, x^29 + 106*x^27 + 48*x^26 + 83*x^25 + 112*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 80*x^18 + 35*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 49*x^9 + 16*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 48*x^2 + 89*x + 112, x^29 + 106*x^27 + 68*x^26 + 11*x^25 + 36*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 12*x^18 + 107*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 121*x^9 + 124*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 20*x^2 + 17*x + 20, x^29 + 106*x^27 + 44*x^26 + 27*x^25 + 92*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 68*x^18 + 91*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 105*x^9 + 4*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 28*x^2 + 33*x + 108, x^29 + 106*x^27 + 76*x^26 + 59*x^25 + 124*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 100*x^18 + 123*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 73*x^9 + 100*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 124*x^2 + x + 76, x^29 + 106*x^27 + 20*x^26 + 11*x^25 + 116*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 60*x^18 + 43*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 121*x^9 + 44*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 100*x^2 + 81*x + 100, x^29 + 106*x^27 + 76*x^26 + 123*x^25 + 28*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 100*x^18 + 59*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 9*x^9 + 68*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 124*x^2 + 65*x + 108, x^29 + 106*x^27 + 8*x^26 + 19*x^25 + 104*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 24*x^18 + 99*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 113*x^9 + 88*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 40*x^2 + 25*x + 72, x^29 + 106*x^27 + 80*x^26 + 3*x^25 + 32*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 22*x^19 + 48*x^18 + 115*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + x^9 + 96*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 74*x^3 + 80*x^2 + 9*x + 96, x^29 + 106*x^27 + 16*x^26 + 51*x^25 + 80*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 112*x^18 + 67*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 81*x^9 + 48*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 16*x^2 + 57*x + 80, x^29 + 106*x^27 + 56*x^26 + 99*x^25 + 72*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 104*x^18 + 83*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 33*x^9 + 120*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 88*x^2 + 41*x + 104, x^29 + 106*x^27 + 112*x^26 + 19*x^25 + 16*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 16*x^18 + 99*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 113*x^9 + 112*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 112*x^2 + 25*x + 16, x^29 + 106*x^27 + 56*x^26 + 35*x^25 + 72*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 40*x^18 + 83*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 97*x^9 + 120*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 24*x^2 + 41*x + 40, x^29 + 106*x^27 + 24*x^26 + 115*x^25 + 24*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 8*x^18 + 67*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 17*x^9 + 40*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 56*x^2 + 57*x + 120, x^29 + 106*x^27 + 76*x^26 + 91*x^25 + 60*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 100*x^18 + 91*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 41*x^9 + 36*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 124*x^2 + 33*x + 12, x^29 + 106*x^27 + 8*x^26 + 99*x^25 + 120*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 88*x^18 + 83*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 33*x^9 + 72*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 104*x^2 + 41*x + 88, x^29 + 106*x^27 + 108*x^26 + 59*x^25 + 92*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 68*x^18 + 123*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 73*x^9 + 4*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 28*x^2 + x + 44, x^29 + 106*x^27 + 28*x^26 + 59*x^25 + 108*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 84*x^18 + 123*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 73*x^9 + 116*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 12*x^2 + x + 124, x^29 + 106*x^27 + 104*x^26 + 3*x^25 + 120*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 120*x^18 + 51*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + x^9 + 72*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 72*x^2 + 73*x + 88, x^29 + 106*x^27 + 4*x^26 + 107*x^25 + 68*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 76*x^18 + 11*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 25*x^9 + 92*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 84*x^2 + 113*x + 52, x^29 + 106*x^27 + 4*x^26 + 11*x^25 + 68*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 76*x^18 + 107*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 121*x^9 + 92*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 84*x^2 + 17*x + 52, x^29 + 106*x^27 + 104*x^26 + 3*x^25 + 24*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 120*x^18 + 51*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + x^9 + 40*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 72*x^2 + 73*x + 120, x^29 + 106*x^27 + 40*x^26 + 67*x^25 + 56*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 56*x^18 + 115*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 65*x^9 + 8*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 8*x^2 + 9*x + 24, x^29 + 106*x^27 + 76*x^26 + 123*x^25 + 92*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 100*x^18 + 59*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 9*x^9 + 4*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 124*x^2 + 65*x + 44, x^29 + 106*x^27 + 72*x^26 + 67*x^25 + 120*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 24*x^18 + 115*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 65*x^9 + 72*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 40*x^2 + 9*x + 88, x^29 + 106*x^27 + 100*x^26 + 11*x^25 + 100*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 108*x^18 + 107*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 121*x^9 + 60*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 52*x^2 + 17*x + 84, x^29 + 106*x^27 + 116*x^26 + 75*x^25 + 52*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 28*x^18 + 43*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 57*x^9 + 108*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 4*x^2 + 81*x + 100, x^29 + 106*x^27 + 76*x^26 + 59*x^25 + 28*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 36*x^18 + 59*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 73*x^9 + 68*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 60*x^2 + 65*x + 44, x^29 + 106*x^27 + 88*x^26 + 35*x^25 + 8*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 72*x^18 + 19*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 97*x^9 + 56*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 120*x^2 + 105*x + 40, x^29 + 106*x^27 + 8*x^26 + 51*x^25 + 72*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 88*x^18 + 3*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 81*x^9 + 120*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 104*x^2 + 121*x + 104, x^29 + 106*x^27 + 116*x^26 + 43*x^25 + 20*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 92*x^18 + 11*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 89*x^9 + 12*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 68*x^2 + 113*x + 4, x^29 + 106*x^27 + 48*x^26 + 67*x^25 + 32*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 16*x^18 + 115*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 65*x^9 + 96*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 112*x^2 + 9*x + 32, x^29 + 106*x^27 + 44*x^26 + 107*x^25 + 76*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 68*x^18 + 11*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 25*x^9 + 20*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 28*x^2 + 113*x + 28, x^29 + 106*x^27 + 8*x^26 + 51*x^25 + 40*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 24*x^18 + 67*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 81*x^9 + 24*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 40*x^2 + 57*x + 8, x^29 + 106*x^27 + 120*x^26 + 99*x^25 + 8*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 104*x^18 + 19*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 33*x^9 + 56*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 88*x^2 + 105*x + 104, x^29 + 106*x^27 + 84*x^26 + 43*x^25 + 20*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 60*x^18 + 75*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 89*x^9 + 12*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 100*x^2 + 49*x + 68, x^29 + 106*x^27 + 60*x^26 + 11*x^25 + 28*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 52*x^18 + 43*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 121*x^9 + 68*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 44*x^2 + 81*x + 108, x^29 + 106*x^27 + 116*x^26 + 91*x^25 + 68*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 92*x^18 + 91*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 41*x^9 + 92*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 68*x^2 + 33*x + 116, x^29 + 106*x^27 + 68*x^26 + 123*x^25 + 20*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 76*x^18 + 59*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 9*x^9 + 12*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 84*x^2 + 65*x + 4, x^29 + 106*x^27 + 100*x^26 + 43*x^25 + 68*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 44*x^18 + 11*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 89*x^9 + 92*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 116*x^2 + 113*x + 116, x^29 + 106*x^27 + 68*x^26 + 91*x^25 + 116*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 12*x^18 + 27*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 41*x^9 + 44*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 20*x^2 + 97*x + 36, x^29 + 106*x^27 + 104*x^26 + 83*x^25 + 8*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 120*x^18 + 99*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 49*x^9 + 56*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 72*x^2 + 25*x + 40, x^29 + 106*x^27 + 12*x^26 + 91*x^25 + 60*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 100*x^18 + 27*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 41*x^9 + 36*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 124*x^2 + 97*x + 76, x^29 + 106*x^27 + 108*x^26 + 91*x^25 + 28*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 4*x^18 + 27*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 41*x^9 + 68*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 92*x^2 + 97*x + 44, x^29 + 106*x^27 + 100*x^26 + 11*x^25 + 100*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 44*x^18 + 43*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 121*x^9 + 60*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 116*x^2 + 81*x + 20, x^29 + 106*x^27 + 32*x^26 + 51*x^25 + 64*x^24 + 36*x^23 + 121*x^21 + 64*x^20 + 86*x^19 + 32*x^18 + 67*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 81*x^9 + 64*x^8 + 36*x^7 + 107*x^5 + 64*x^4 + 10*x^3 + 96*x^2 + 57*x, x^29 + 106*x^27 + 72*x^26 + 83*x^25 + 40*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 88*x^18 + 35*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 49*x^9 + 24*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 104*x^2 + 89*x + 8, x^29 + 106*x^27 + 64*x^26 + 51*x^25 + 64*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 86*x^19 + 67*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 81*x^9 + 64*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 10*x^3 + 57*x, x^29 + 106*x^27 + 12*x^26 + 43*x^25 + 12*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 36*x^18 + 11*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 89*x^9 + 84*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 60*x^2 + 113*x + 28, x^29 + 106*x^27 + 44*x^26 + 91*x^25 + 60*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 68*x^18 + 27*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 41*x^9 + 36*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 28*x^2 + 97*x + 76, x^29 + 106*x^27 + 51*x^25 + 64*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 86*x^19 + 64*x^18 + 67*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 81*x^9 + 64*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 10*x^3 + 64*x^2 + 57*x, x^29 + 106*x^27 + 88*x^26 + 51*x^25 + 120*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 8*x^18 + 67*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 81*x^9 + 72*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 56*x^2 + 57*x + 24, x^29 + 106*x^27 + 100*x^26 + 123*x^25 + 20*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 44*x^18 + 59*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 9*x^9 + 12*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 116*x^2 + 65*x + 4, x^29 + 106*x^27 + 44*x^26 + 123*x^25 + 124*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 68*x^18 + 123*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 9*x^9 + 100*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 28*x^2 + x + 12, x^29 + 106*x^27 + 32*x^26 + 51*x^25 + 100*x^23 + 64*x^22 + 57*x^21 + 22*x^19 + 96*x^18 + 3*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 81*x^9 + 100*x^7 + 64*x^6 + 43*x^5 + 74*x^3 + 32*x^2 + 121*x, x^29 + 106*x^27 + 108*x^26 + 75*x^25 + 44*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 68*x^18 + 107*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 57*x^9 + 52*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 28*x^2 + 17*x + 60, x^29 + 106*x^27 + 24*x^26 + 83*x^25 + 120*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 72*x^18 + 35*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 49*x^9 + 72*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 120*x^2 + 89*x + 24, x^29 + 106*x^27 + 96*x^26 + 19*x^25 + 32*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 22*x^19 + 32*x^18 + 35*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 113*x^9 + 96*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 74*x^3 + 96*x^2 + 89*x + 32, x^29 + 106*x^27 + 48*x^26 + 99*x^25 + 64*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 80*x^18 + 19*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 33*x^9 + 64*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 48*x^2 + 105*x, x^29 + 106*x^27 + 108*x^26 + 107*x^25 + 44*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 68*x^18 + 75*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 25*x^9 + 52*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 28*x^2 + 49*x + 60, x^29 + 106*x^27 + 28*x^26 + 123*x^25 + 108*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 84*x^18 + 59*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 9*x^9 + 116*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 12*x^2 + 65*x + 124, x^29 + 106*x^27 + 108*x^26 + 43*x^25 + 108*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 68*x^18 + 11*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 89*x^9 + 116*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 28*x^2 + 113*x + 124, x^29 + 106*x^27 + 48*x^26 + 67*x^25 + 96*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 16*x^18 + 115*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 65*x^9 + 32*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 112*x^2 + 9*x + 96, x^29 + 106*x^27 + 80*x^26 + 83*x^25 + 16*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 48*x^18 + 35*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 49*x^9 + 112*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 80*x^2 + 89*x + 16, x^29 + 106*x^27 + 112*x^26 + 35*x^25 + 32*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 22*x^19 + 16*x^18 + 83*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 97*x^9 + 96*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 74*x^3 + 112*x^2 + 41*x + 96, x^29 + 106*x^27 + 56*x^26 + 115*x^25 + 24*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 40*x^18 + 3*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 17*x^9 + 40*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 24*x^2 + 121*x + 56, x^29 + 106*x^27 + 32*x^26 + 115*x^25 + 64*x^24 + 36*x^23 + 121*x^21 + 64*x^20 + 86*x^19 + 32*x^18 + 3*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 17*x^9 + 64*x^8 + 36*x^7 + 107*x^5 + 64*x^4 + 10*x^3 + 96*x^2 + 121*x, x^29 + 106*x^27 + 20*x^26 + 27*x^25 + 100*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 60*x^18 + 27*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 105*x^9 + 60*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 100*x^2 + 97*x + 20, x^29 + 106*x^27 + 76*x^26 + 91*x^25 + 124*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 36*x^18 + 27*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 41*x^9 + 100*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 60*x^2 + 97*x + 12, x^29 + 106*x^27 + 20*x^26 + 59*x^25 + 68*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 124*x^18 + 59*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 73*x^9 + 92*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 36*x^2 + 65*x + 52, x^29 + 106*x^27 + 24*x^26 + 3*x^25 + 40*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 72*x^18 + 115*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + x^9 + 24*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 120*x^2 + 9*x + 8, x^29 + 106*x^27 + 104*x^26 + 83*x^25 + 72*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 56*x^18 + 35*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 49*x^9 + 120*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 8*x^2 + 89*x + 40, x^29 + 106*x^27 + 108*x^26 + 123*x^25 + 28*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 68*x^18 + 59*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 9*x^9 + 68*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 28*x^2 + 65*x + 108, x^29 + 106*x^27 + 108*x^26 + 59*x^25 + 60*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 68*x^18 + 123*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 73*x^9 + 36*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 28*x^2 + x + 12, x^29 + 106*x^27 + 112*x^26 + 99*x^25 + 32*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 22*x^19 + 16*x^18 + 19*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 33*x^9 + 96*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 74*x^3 + 112*x^2 + 105*x + 96, x^29 + 106*x^27 + 48*x^26 + 51*x^25 + 80*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 80*x^18 + 67*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 81*x^9 + 48*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 48*x^2 + 57*x + 80, x^29 + 106*x^27 + 52*x^26 + 107*x^25 + 52*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 28*x^18 + 75*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 25*x^9 + 108*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 4*x^2 + 49*x + 36, x^29 + 106*x^27 + 48*x^26 + 19*x^25 + 48*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 80*x^18 + 99*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 113*x^9 + 80*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 48*x^2 + 25*x + 48, x^29 + 106*x^27 + 36*x^26 + 91*x^25 + 52*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 108*x^18 + 91*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 41*x^9 + 108*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 52*x^2 + 33*x + 36, x^29 + 106*x^27 + 84*x^26 + 107*x^25 + 52*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 60*x^18 + 11*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 25*x^9 + 108*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 100*x^2 + 113*x + 100, x^29 + 106*x^27 + 92*x^26 + 91*x^25 + 12*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 20*x^18 + 91*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 41*x^9 + 84*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 76*x^2 + 33*x + 28, x^29 + 106*x^27 + 96*x^26 + 83*x^25 + 96*x^24 + 36*x^23 + 57*x^21 + 86*x^19 + 96*x^18 + 35*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 49*x^9 + 32*x^8 + 36*x^7 + 43*x^5 + 10*x^3 + 32*x^2 + 89*x + 32, x^29 + 106*x^27 + 96*x^26 + 115*x^25 + 32*x^24 + 36*x^23 + 121*x^21 + 86*x^19 + 96*x^18 + 3*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 17*x^9 + 96*x^8 + 36*x^7 + 107*x^5 + 10*x^3 + 32*x^2 + 121*x + 96, x^29 + 106*x^27 + 112*x^26 + 67*x^25 + 100*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 16*x^18 + 51*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 65*x^9 + 100*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 112*x^2 + 73*x + 64, x^29 + 106*x^27 + 112*x^26 + 51*x^25 + 80*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 80*x^18 + 3*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 81*x^9 + 48*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 48*x^2 + 121*x + 16, x^29 + 106*x^27 + 48*x^26 + 115*x^25 + 48*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 80*x^18 + 3*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 17*x^9 + 80*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 48*x^2 + 121*x + 48, x^29 + 106*x^27 + 40*x^26 + 83*x^25 + 8*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 120*x^18 + 35*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 49*x^9 + 56*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 72*x^2 + 89*x + 104, x^29 + 106*x^27 + 60*x^26 + 91*x^25 + 76*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 52*x^18 + 91*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 41*x^9 + 20*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 44*x^2 + 33*x + 92, x^29 + 106*x^27 + 72*x^26 + 3*x^25 + 56*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 88*x^18 + 115*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + x^9 + 8*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 104*x^2 + 9*x + 88, x^29 + 106*x^27 + 104*x^26 + 35*x^25 + 24*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 120*x^18 + 19*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 97*x^9 + 40*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 72*x^2 + 105*x + 120, x^29 + 106*x^27 + 24*x^26 + 19*x^25 + 56*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 8*x^18 + 35*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 113*x^9 + 8*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 56*x^2 + 89*x + 24, x^29 + 106*x^27 + 48*x^26 + 99*x^25 + 96*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 22*x^19 + 80*x^18 + 19*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 33*x^9 + 32*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 74*x^3 + 48*x^2 + 105*x + 32, x^29 + 106*x^27 + 20*x^26 + 107*x^25 + 52*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 60*x^18 + 75*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 25*x^9 + 108*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 100*x^2 + 49*x + 36, x^29 + 106*x^27 + 24*x^26 + 51*x^25 + 88*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 72*x^18 + 67*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 81*x^9 + 104*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 120*x^2 + 57*x + 120, x^29 + 106*x^27 + 12*x^26 + 123*x^25 + 124*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 100*x^18 + 123*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 9*x^9 + 100*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 124*x^2 + x + 12, x^29 + 106*x^27 + 104*x^26 + 83*x^25 + 40*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 56*x^18 + 35*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 49*x^9 + 24*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 8*x^2 + 89*x + 8, x^29 + 106*x^27 + 4*x^26 + 27*x^25 + 116*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 12*x^18 + 27*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 105*x^9 + 44*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 20*x^2 + 97*x + 100, x^29 + 106*x^27 + 104*x^26 + 83*x^25 + 72*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 120*x^18 + 99*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 49*x^9 + 120*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 72*x^2 + 25*x + 104, x^29 + 106*x^27 + 68*x^26 + 27*x^25 + 52*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 12*x^18 + 91*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 105*x^9 + 108*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 20*x^2 + 33*x + 100, x^29 + 106*x^27 + 96*x^26 + 3*x^25 + 16*x^24 + 100*x^23 + 25*x^21 + 32*x^20 + 22*x^19 + 96*x^18 + 115*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + x^9 + 112*x^8 + 100*x^7 + 11*x^5 + 32*x^4 + 74*x^3 + 32*x^2 + 9*x + 16, x^29 + 106*x^27 + 60*x^26 + 59*x^25 + 76*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 116*x^18 + 59*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 73*x^9 + 20*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 108*x^2 + 65*x + 28, x^29 + 106*x^27 + 8*x^26 + 19*x^25 + 72*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 88*x^18 + 35*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 113*x^9 + 120*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 104*x^2 + 89*x + 104, x^29 + 106*x^27 + 116*x^26 + 27*x^25 + 100*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 28*x^18 + 91*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 105*x^9 + 60*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 4*x^2 + 33*x + 84, x^29 + 106*x^27 + 88*x^26 + 35*x^25 + 40*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 72*x^18 + 19*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 97*x^9 + 24*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 120*x^2 + 105*x + 72, x^29 + 106*x^27 + 92*x^26 + 75*x^25 + 124*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 84*x^18 + 43*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 57*x^9 + 100*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 12*x^2 + 81*x + 12, x^29 + 106*x^27 + 112*x^26 + 51*x^25 + 16*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 16*x^18 + 67*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 81*x^9 + 112*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 112*x^2 + 57*x + 16, x^29 + 106*x^27 + 48*x^26 + 67*x^25 + 64*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 86*x^19 + 16*x^18 + 115*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 65*x^9 + 64*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 10*x^3 + 112*x^2 + 9*x + 64, x^29 + 106*x^27 + 84*x^26 + 11*x^25 + 52*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 124*x^18 + 43*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 121*x^9 + 108*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 36*x^2 + 81*x + 36, x^29 + 106*x^27 + 76*x^26 + 123*x^25 + 60*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 36*x^18 + 123*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 9*x^9 + 36*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 60*x^2 + x + 76, x^29 + 106*x^27 + 76*x^26 + 123*x^25 + 92*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 36*x^18 + 123*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 9*x^9 + 4*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 60*x^2 + x + 108, x^29 + 106*x^27 + 112*x^26 + 3*x^25 + 100*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 16*x^18 + 115*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + x^9 + 100*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 112*x^2 + 9*x + 64, x^29 + 106*x^27 + 60*x^26 + 27*x^25 + 44*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 52*x^18 + 27*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 105*x^9 + 52*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 44*x^2 + 97*x + 60, x^29 + 106*x^27 + 108*x^26 + 59*x^25 + 124*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 4*x^18 + 59*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 73*x^9 + 100*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 92*x^2 + 65*x + 12, x^29 + 106*x^27 + 68*x^26 + 59*x^25 + 52*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 76*x^18 + 123*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 73*x^9 + 108*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 84*x^2 + x + 36, x^29 + 106*x^27 + 20*x^26 + 123*x^25 + 4*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 124*x^18 + 123*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 9*x^9 + 28*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 36*x^2 + x + 116, x^29 + 106*x^27 + 64*x^26 + 67*x^25 + 16*x^24 + 36*x^23 + 89*x^21 + 96*x^20 + 86*x^19 + 64*x^18 + 115*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 65*x^9 + 112*x^8 + 36*x^7 + 75*x^5 + 96*x^4 + 10*x^3 + 64*x^2 + 9*x + 80, x^29 + 106*x^27 + 96*x^26 + 115*x^25 + 100*x^23 + 64*x^22 + 57*x^21 + 22*x^19 + 32*x^18 + 67*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 17*x^9 + 100*x^7 + 64*x^6 + 43*x^5 + 74*x^3 + 96*x^2 + 57*x, x^29 + 106*x^27 + 60*x^26 + 123*x^25 + 108*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 52*x^18 + 59*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 9*x^9 + 116*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 44*x^2 + 65*x + 124, x^29 + 106*x^27 + 36*x^26 + 27*x^25 + 20*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 44*x^18 + 91*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 105*x^9 + 12*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 116*x^2 + 33*x + 68, x^29 + 106*x^27 + 32*x^26 + 67*x^25 + 48*x^24 + 100*x^23 + 25*x^21 + 96*x^20 + 22*x^19 + 32*x^18 + 51*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 65*x^9 + 80*x^8 + 100*x^7 + 11*x^5 + 96*x^4 + 74*x^3 + 96*x^2 + 73*x + 48, x^29 + 106*x^27 + 100*x^26 + 75*x^25 + 100*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 44*x^18 + 107*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 57*x^9 + 60*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 116*x^2 + 17*x + 20, x^29 + 106*x^27 + 120*x^26 + 51*x^25 + 24*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 104*x^18 + 67*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 81*x^9 + 40*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 88*x^2 + 57*x + 56, x^29 + 106*x^27 + 100*x^26 + 107*x^25 + 36*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 108*x^18 + 11*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 25*x^9 + 124*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 52*x^2 + 113*x + 20, x^29 + 106*x^27 + 104*x^26 + 51*x^25 + 104*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 120*x^18 + 3*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 81*x^9 + 88*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 72*x^2 + 121*x + 8, x^29 + 106*x^27 + 12*x^26 + 91*x^25 + 124*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 36*x^18 + 91*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 41*x^9 + 100*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 60*x^2 + 33*x + 76, x^29 + 106*x^27 + 36*x^26 + 11*x^25 + 100*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 44*x^18 + 107*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 121*x^9 + 60*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 116*x^2 + 17*x + 84, x^29 + 106*x^27 + 56*x^26 + 35*x^25 + 40*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 40*x^18 + 83*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 97*x^9 + 24*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 24*x^2 + 41*x + 8, x^29 + 106*x^27 + 124*x^26 + 27*x^25 + 44*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 52*x^18 + 91*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 105*x^9 + 52*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 44*x^2 + 33*x + 124, x^29 + 106*x^27 + 20*x^26 + 91*x^25 + 68*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 124*x^18 + 27*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 41*x^9 + 92*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 36*x^2 + 97*x + 52, x^29 + 106*x^27 + 60*x^26 + 107*x^25 + 92*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 52*x^18 + 75*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 25*x^9 + 4*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 44*x^2 + 49*x + 44, x^29 + 106*x^27 + 112*x^26 + 3*x^25 + 96*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 22*x^19 + 16*x^18 + 115*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + x^9 + 32*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 74*x^3 + 112*x^2 + 9*x + 32, x^29 + 106*x^27 + 16*x^26 + 115*x^25 + 16*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 112*x^18 + 3*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 17*x^9 + 112*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 16*x^2 + 121*x + 16, x^29 + 106*x^27 + 28*x^26 + 75*x^25 + 60*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 84*x^18 + 107*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 57*x^9 + 36*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 12*x^2 + 17*x + 12, x^29 + 106*x^27 + 72*x^26 + 67*x^25 + 120*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 88*x^18 + 51*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 65*x^9 + 72*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 104*x^2 + 73*x + 24, x^29 + 106*x^27 + 40*x^26 + 35*x^25 + 56*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 120*x^18 + 83*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 97*x^9 + 8*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 72*x^2 + 41*x + 88, x^29 + 106*x^27 + 16*x^26 + 99*x^25 + 36*x^23 + 96*x^22 + 25*x^21 + 86*x^19 + 48*x^18 + 83*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 33*x^9 + 36*x^7 + 96*x^6 + 11*x^5 + 10*x^3 + 80*x^2 + 41*x, x^29 + 106*x^27 + 24*x^26 + 35*x^25 + 40*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 8*x^18 + 19*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 97*x^9 + 24*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 56*x^2 + 105*x + 72, x^29 + 106*x^27 + 120*x^26 + 83*x^25 + 88*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 40*x^18 + 99*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 49*x^9 + 104*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 24*x^2 + 25*x + 56, x^29 + 106*x^27 + 56*x^26 + 83*x^25 + 24*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 40*x^18 + 35*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 49*x^9 + 40*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 24*x^2 + 89*x + 56, x^29 + 106*x^27 + 12*x^26 + 123*x^25 + 28*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 100*x^18 + 123*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 9*x^9 + 68*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 124*x^2 + x + 44, x^29 + 106*x^27 + 52*x^26 + 43*x^25 + 20*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 92*x^18 + 75*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 89*x^9 + 12*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 68*x^2 + 49*x + 68, x^29 + 106*x^27 + 40*x^26 + 115*x^25 + 8*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 56*x^18 + 67*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 17*x^9 + 56*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 8*x^2 + 57*x + 40, x^29 + 106*x^27 + 76*x^26 + 91*x^25 + 28*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 36*x^18 + 27*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 41*x^9 + 68*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 60*x^2 + 97*x + 44, x^29 + 106*x^27 + 64*x^26 + 67*x^25 + 80*x^24 + 36*x^23 + 89*x^21 + 96*x^20 + 86*x^19 + 64*x^18 + 115*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 65*x^9 + 48*x^8 + 36*x^7 + 75*x^5 + 96*x^4 + 10*x^3 + 64*x^2 + 9*x + 16, x^29 + 106*x^27 + 48*x^26 + 51*x^25 + 16*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 16*x^18 + 3*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 81*x^9 + 112*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 112*x^2 + 121*x + 80, x^29 + 106*x^27 + 108*x^26 + 43*x^25 + 108*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 4*x^18 + 75*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 89*x^9 + 116*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 92*x^2 + 49*x + 60, x^29 + 106*x^27 + 124*x^26 + 27*x^25 + 108*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 116*x^18 + 27*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 105*x^9 + 116*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 108*x^2 + 97*x + 124, x^29 + 106*x^27 + 16*x^26 + 19*x^25 + 48*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 112*x^18 + 99*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 113*x^9 + 80*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 16*x^2 + 25*x + 48, x^29 + 106*x^27 + 112*x^26 + 51*x^25 + 48*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 80*x^18 + 3*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 81*x^9 + 80*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 48*x^2 + 121*x + 112, x^29 + 106*x^27 + 48*x^26 + 3*x^25 + 96*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 16*x^18 + 51*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + x^9 + 32*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 112*x^2 + 73*x + 96, x^29 + 106*x^27 + 84*x^26 + 75*x^25 + 84*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 124*x^18 + 107*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 57*x^9 + 76*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 36*x^2 + 17*x + 68, x^29 + 106*x^27 + 112*x^26 + 35*x^25 + 32*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 80*x^18 + 19*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 97*x^9 + 96*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 48*x^2 + 105*x + 32, x^29 + 106*x^27 + 40*x^26 + 51*x^25 + 8*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 120*x^18 + 67*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 81*x^9 + 56*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 72*x^2 + 57*x + 104, x^29 + 106*x^27 + 32*x^26 + 35*x^25 + 112*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 86*x^19 + 96*x^18 + 19*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 97*x^9 + 16*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 10*x^3 + 32*x^2 + 105*x + 48, x^29 + 106*x^27 + 72*x^26 + 51*x^25 + 40*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 24*x^18 + 3*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 81*x^9 + 24*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 40*x^2 + 121*x + 72, x^29 + 106*x^27 + 76*x^26 + 123*x^25 + 60*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 100*x^18 + 59*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 9*x^9 + 36*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 124*x^2 + 65*x + 12, x^29 + 106*x^27 + 68*x^26 + 43*x^25 + 36*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 76*x^18 + 11*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 89*x^9 + 124*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 84*x^2 + 113*x + 84, x^29 + 106*x^27 + 92*x^26 + 107*x^25 + 92*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 84*x^18 + 11*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 25*x^9 + 4*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 12*x^2 + 113*x + 108, x^29 + 106*x^27 + 36*x^26 + 75*x^25 + 4*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 108*x^18 + 107*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 57*x^9 + 28*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 52*x^2 + 17*x + 52, x^29 + 106*x^27 + 96*x^26 + 35*x^25 + 80*x^24 + 100*x^23 + 89*x^21 + 32*x^20 + 22*x^19 + 96*x^18 + 83*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 97*x^9 + 48*x^8 + 100*x^7 + 75*x^5 + 32*x^4 + 74*x^3 + 32*x^2 + 41*x + 80, x^29 + 106*x^27 + 56*x^26 + 115*x^25 + 120*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 40*x^18 + 3*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 17*x^9 + 72*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 24*x^2 + 121*x + 24, x^29 + 106*x^27 + 4*x^26 + 27*x^25 + 84*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 12*x^18 + 27*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 105*x^9 + 76*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 20*x^2 + 97*x + 68, x^29 + 106*x^27 + 44*x^26 + 91*x^25 + 124*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 68*x^18 + 27*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 41*x^9 + 100*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 28*x^2 + 97*x + 12, x^29 + 106*x^27 + 40*x^26 + 83*x^25 + 8*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 56*x^18 + 99*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 49*x^9 + 56*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 8*x^2 + 25*x + 40, x^29 + 106*x^27 + 76*x^26 + 11*x^25 + 12*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 36*x^18 + 107*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 121*x^9 + 84*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 60*x^2 + 17*x + 92, x^29 + 106*x^27 + 36*x^26 + 123*x^25 + 52*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 108*x^18 + 59*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 9*x^9 + 108*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 52*x^2 + 65*x + 36, x^29 + 106*x^27 + 48*x^26 + 35*x^25 + 100*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 80*x^18 + 83*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 97*x^9 + 100*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 48*x^2 + 41*x + 64, x^29 + 106*x^27 + 56*x^26 + 35*x^25 + 72*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 104*x^18 + 19*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 97*x^9 + 120*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 88*x^2 + 105*x + 104, x^29 + 106*x^27 + 16*x^26 + 51*x^25 + 48*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 112*x^18 + 67*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 81*x^9 + 80*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 16*x^2 + 57*x + 48, x^29 + 106*x^27 + 12*x^26 + 75*x^25 + 44*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 100*x^18 + 43*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 57*x^9 + 52*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 124*x^2 + 81*x + 124, x^29 + 106*x^27 + 104*x^26 + 67*x^25 + 24*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 120*x^18 + 115*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 65*x^9 + 40*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 72*x^2 + 9*x + 120, x^29 + 106*x^27 + 88*x^26 + 115*x^25 + 24*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 72*x^18 + 67*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 17*x^9 + 40*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 120*x^2 + 57*x + 120, x^29 + 106*x^27 + 112*x^26 + 67*x^25 + 96*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 22*x^19 + 16*x^18 + 51*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 65*x^9 + 32*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 74*x^3 + 112*x^2 + 73*x + 32, x^29 + 106*x^27 + 120*x^26 + 19*x^25 + 88*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 104*x^18 + 99*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 113*x^9 + 104*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 88*x^2 + 25*x + 120, x^29 + 106*x^27 + 84*x^26 + 75*x^25 + 20*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 60*x^18 + 43*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 57*x^9 + 12*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 100*x^2 + 81*x + 68, x^29 + 106*x^27 + 72*x^26 + 51*x^25 + 104*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 88*x^18 + 67*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 81*x^9 + 88*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 104*x^2 + 57*x + 72, x^29 + 106*x^27 + 36*x^26 + 43*x^25 + 100*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 44*x^18 + 75*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 89*x^9 + 60*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 116*x^2 + 49*x + 84, x^29 + 106*x^27 + 32*x^26 + 35*x^25 + 48*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 86*x^19 + 96*x^18 + 19*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 97*x^9 + 80*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 10*x^3 + 32*x^2 + 105*x + 112, x^29 + 106*x^27 + 20*x^26 + 91*x^25 + 4*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 124*x^18 + 27*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 41*x^9 + 28*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 36*x^2 + 97*x + 116, x^29 + 106*x^27 + 56*x^26 + 115*x^25 + 88*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 104*x^18 + 67*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 17*x^9 + 104*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 88*x^2 + 57*x + 56, x^29 + 106*x^27 + 16*x^26 + 3*x^25 + 36*x^23 + 96*x^22 + 89*x^21 + 86*x^19 + 48*x^18 + 51*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + x^9 + 36*x^7 + 96*x^6 + 75*x^5 + 10*x^3 + 80*x^2 + 73*x, x^29 + 106*x^27 + 40*x^26 + 83*x^25 + 104*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 120*x^18 + 35*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 49*x^9 + 88*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 72*x^2 + 89*x + 72, x^29 + 106*x^27 + 104*x^26 + 51*x^25 + 72*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 120*x^18 + 3*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 81*x^9 + 120*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 72*x^2 + 121*x + 104, x^29 + 106*x^27 + 44*x^26 + 11*x^25 + 12*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 4*x^18 + 43*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 121*x^9 + 84*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 92*x^2 + 81*x + 28, x^29 + 106*x^27 + 124*x^26 + 123*x^25 + 76*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 52*x^18 + 123*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 9*x^9 + 20*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 44*x^2 + x + 28, x^29 + 106*x^27 + 104*x^26 + 99*x^25 + 56*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 56*x^18 + 19*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 33*x^9 + 8*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 8*x^2 + 105*x + 88, x^29 + 106*x^27 + 92*x^26 + 59*x^25 + 12*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 84*x^18 + 59*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 73*x^9 + 84*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 12*x^2 + 65*x + 92, x^29 + 106*x^27 + 112*x^26 + 35*x^25 + 36*x^23 + 32*x^22 + 25*x^21 + 86*x^19 + 80*x^18 + 19*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 97*x^9 + 36*x^7 + 32*x^6 + 11*x^5 + 10*x^3 + 48*x^2 + 105*x, x^29 + 106*x^27 + 40*x^26 + 99*x^25 + 24*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 120*x^18 + 19*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 33*x^9 + 40*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 72*x^2 + 105*x + 56, x^29 + 106*x^27 + 36*x^26 + 59*x^25 + 84*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 108*x^18 + 123*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 73*x^9 + 76*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 52*x^2 + x + 68, x^29 + 106*x^27 + 104*x^26 + 3*x^25 + 88*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 120*x^18 + 51*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + x^9 + 104*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 72*x^2 + 73*x + 56, x^29 + 106*x^27 + 104*x^26 + 67*x^25 + 120*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 56*x^18 + 51*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 65*x^9 + 72*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 8*x^2 + 73*x + 24, x^29 + 106*x^27 + 68*x^26 + 59*x^25 + 84*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 76*x^18 + 123*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 73*x^9 + 76*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 84*x^2 + x + 68, x^29 + 106*x^27 + 56*x^26 + 99*x^25 + 72*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 40*x^18 + 19*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 33*x^9 + 120*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 24*x^2 + 105*x + 40, x^29 + 106*x^27 + 24*x^26 + 83*x^25 + 120*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 8*x^18 + 99*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 49*x^9 + 72*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 56*x^2 + 25*x + 88, x^29 + 106*x^27 + 24*x^26 + 115*x^25 + 56*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 72*x^18 + 3*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 17*x^9 + 8*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 120*x^2 + 121*x + 88, x^29 + 106*x^27 + 60*x^26 + 27*x^25 + 76*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 116*x^18 + 91*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 105*x^9 + 20*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 108*x^2 + 33*x + 28, x^29 + 106*x^27 + 104*x^26 + 115*x^25 + 8*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 120*x^18 + 67*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 17*x^9 + 56*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 72*x^2 + 57*x + 40, x^29 + 106*x^27 + 48*x^26 + 3*x^25 + 96*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 22*x^19 + 80*x^18 + 115*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + x^9 + 32*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 74*x^3 + 48*x^2 + 9*x + 32, x^29 + 106*x^27 + 24*x^26 + 83*x^25 + 88*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 8*x^18 + 99*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 49*x^9 + 104*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 56*x^2 + 25*x + 56, x^29 + 106*x^27 + 44*x^26 + 43*x^25 + 108*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 4*x^18 + 11*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 89*x^9 + 116*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 92*x^2 + 113*x + 124, x^29 + 106*x^27 + 12*x^26 + 91*x^25 + 124*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 100*x^18 + 27*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 41*x^9 + 100*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 124*x^2 + 97*x + 12, x^29 + 106*x^27 + 56*x^26 + 67*x^25 + 40*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 40*x^18 + 51*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 65*x^9 + 24*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 24*x^2 + 73*x + 8, x^29 + 106*x^27 + 8*x^26 + 83*x^25 + 8*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 24*x^18 + 35*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 49*x^9 + 56*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 40*x^2 + 89*x + 104, x^29 + 106*x^27 + 96*x^26 + 35*x^25 + 112*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 86*x^19 + 32*x^18 + 19*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 97*x^9 + 16*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 10*x^3 + 96*x^2 + 105*x + 48, x^29 + 106*x^27 + 100*x^26 + 43*x^25 + 68*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 108*x^18 + 75*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 89*x^9 + 92*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 52*x^2 + 49*x + 52, x^29 + 106*x^27 + 4*x^26 + 27*x^25 + 20*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 12*x^18 + 27*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 105*x^9 + 12*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 20*x^2 + 97*x + 4, x^29 + 106*x^27 + 68*x^26 + 75*x^25 + 36*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 12*x^18 + 43*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 57*x^9 + 124*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 20*x^2 + 81*x + 20, x^29 + 106*x^27 + 124*x^26 + 123*x^25 + 76*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 116*x^18 + 59*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 9*x^9 + 20*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 108*x^2 + 65*x + 92, x^29 + 106*x^27 + 116*x^26 + 11*x^25 + 84*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 92*x^18 + 43*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 121*x^9 + 76*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 68*x^2 + 81*x + 68, x^29 + 106*x^27 + 100*x^26 + 75*x^25 + 36*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 44*x^18 + 107*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 57*x^9 + 124*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 116*x^2 + 17*x + 84, x^29 + 106*x^27 + 80*x^26 + 19*x^25 + 112*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 48*x^18 + 99*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 113*x^9 + 16*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 80*x^2 + 25*x + 112, x^29 + 106*x^27 + 4*x^26 + 107*x^25 + 4*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 76*x^18 + 11*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 25*x^9 + 28*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 84*x^2 + 113*x + 116, x^29 + 106*x^27 + 48*x^26 + 35*x^25 + 36*x^23 + 32*x^22 + 25*x^21 + 86*x^19 + 16*x^18 + 19*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 97*x^9 + 36*x^7 + 32*x^6 + 11*x^5 + 10*x^3 + 112*x^2 + 105*x, x^29 + 106*x^27 + 40*x^26 + 115*x^25 + 40*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 56*x^18 + 67*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 17*x^9 + 24*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 8*x^2 + 57*x + 72, x^29 + 106*x^27 + 8*x^26 + 99*x^25 + 88*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 88*x^18 + 83*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 33*x^9 + 104*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 104*x^2 + 41*x + 56, x^29 + 106*x^27 + 100*x^26 + 59*x^25 + 116*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 44*x^18 + 123*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 73*x^9 + 44*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 116*x^2 + x + 100, x^29 + 106*x^27 + 36*x^26 + 59*x^25 + 20*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 108*x^18 + 123*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 73*x^9 + 12*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 52*x^2 + x + 4, x^29 + 106*x^27 + 28*x^26 + 11*x^25 + 28*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 20*x^18 + 107*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 121*x^9 + 68*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 76*x^2 + 17*x + 44, x^29 + 106*x^27 + 100*x^26 + 123*x^25 + 116*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 44*x^18 + 59*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 9*x^9 + 44*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 116*x^2 + 65*x + 100, x^29 + 106*x^27 + 56*x^26 + 3*x^25 + 104*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 40*x^18 + 115*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + x^9 + 88*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 24*x^2 + 9*x + 72, x^29 + 106*x^27 + 64*x^26 + 51*x^25 + 100*x^23 + 57*x^21 + 22*x^19 + 64*x^18 + 3*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 81*x^9 + 100*x^7 + 43*x^5 + 74*x^3 + 64*x^2 + 121*x, x^29 + 106*x^27 + 20*x^26 + 75*x^25 + 52*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 124*x^18 + 43*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 57*x^9 + 108*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 36*x^2 + 81*x + 100, x^29 + 106*x^27 + 52*x^26 + 27*x^25 + 4*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 28*x^18 + 27*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 105*x^9 + 28*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 4*x^2 + 97*x + 52, x^29 + 106*x^27 + 120*x^26 + 35*x^25 + 72*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 40*x^18 + 19*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 97*x^9 + 120*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 24*x^2 + 105*x + 104, x^29 + 106*x^27 + 16*x^26 + 19*x^25 + 48*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 48*x^18 + 35*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 113*x^9 + 80*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 80*x^2 + 89*x + 112, x^29 + 106*x^27 + 44*x^26 + 107*x^25 + 108*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 68*x^18 + 11*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 25*x^9 + 116*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 28*x^2 + 113*x + 60, x^29 + 106*x^27 + 120*x^26 + 115*x^25 + 88*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 40*x^18 + 67*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 17*x^9 + 104*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 24*x^2 + 57*x + 56, x^29 + 106*x^27 + 32*x^26 + 83*x^25 + 64*x^24 + 36*x^23 + 57*x^21 + 64*x^20 + 86*x^19 + 32*x^18 + 35*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 49*x^9 + 64*x^8 + 36*x^7 + 43*x^5 + 64*x^4 + 10*x^3 + 96*x^2 + 89*x, x^29 + 106*x^27 + 56*x^26 + 99*x^25 + 8*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 104*x^18 + 83*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 33*x^9 + 56*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 88*x^2 + 41*x + 40, x^29 + 106*x^27 + 24*x^26 + 67*x^25 + 104*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 72*x^18 + 51*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 65*x^9 + 88*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 120*x^2 + 73*x + 72, x^29 + 106*x^27 + 20*x^26 + 59*x^25 + 36*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 124*x^18 + 59*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 73*x^9 + 124*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 36*x^2 + 65*x + 20, x^29 + 106*x^27 + 44*x^26 + 59*x^25 + 124*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 68*x^18 + 59*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 73*x^9 + 100*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 28*x^2 + 65*x + 12, x^29 + 106*x^27 + 28*x^26 + 123*x^25 + 44*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 84*x^18 + 59*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 9*x^9 + 52*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 12*x^2 + 65*x + 60, x^29 + 106*x^27 + 72*x^26 + 19*x^25 + 8*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 88*x^18 + 99*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 113*x^9 + 56*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 104*x^2 + 25*x + 104, x^29 + 106*x^27 + 84*x^26 + 43*x^25 + 84*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 124*x^18 + 11*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 89*x^9 + 76*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 36*x^2 + 113*x + 68, x^29 + 106*x^27 + 24*x^26 + 51*x^25 + 24*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 8*x^18 + 3*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 81*x^9 + 40*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 56*x^2 + 121*x + 120, x^29 + 106*x^27 + 36*x^26 + 123*x^25 + 20*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 108*x^18 + 59*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 9*x^9 + 12*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 52*x^2 + 65*x + 4, x^29 + 106*x^27 + 116*x^26 + 91*x^25 + 36*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 28*x^18 + 27*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 41*x^9 + 124*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 4*x^2 + 97*x + 20, x^29 + 106*x^27 + 56*x^26 + 51*x^25 + 56*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 40*x^18 + 67*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 81*x^9 + 8*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 24*x^2 + 57*x + 88, x^29 + 106*x^27 + 96*x^26 + 83*x^25 + 64*x^24 + 36*x^23 + 57*x^21 + 64*x^20 + 86*x^19 + 96*x^18 + 35*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 49*x^9 + 64*x^8 + 36*x^7 + 43*x^5 + 64*x^4 + 10*x^3 + 32*x^2 + 89*x, x^29 + 106*x^27 + 64*x^26 + 19*x^25 + 64*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 86*x^19 + 99*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 113*x^9 + 64*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 10*x^3 + 25*x, x^29 + 106*x^27 + 8*x^26 + 51*x^25 + 8*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 88*x^18 + 3*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 81*x^9 + 56*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 104*x^2 + 121*x + 40, x^29 + 106*x^27 + 112*x^26 + 99*x^25 + 64*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 86*x^19 + 80*x^18 + 83*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 33*x^9 + 64*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 10*x^3 + 48*x^2 + 41*x + 64, x^29 + 106*x^27 + 68*x^26 + 59*x^25 + 116*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 76*x^18 + 123*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 73*x^9 + 44*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 84*x^2 + x + 100, x^29 + 106*x^27 + 8*x^26 + 99*x^25 + 88*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 24*x^18 + 19*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 33*x^9 + 104*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 40*x^2 + 105*x + 120, x^29 + 106*x^27 + 96*x^26 + 83*x^25 + 64*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 22*x^19 + 32*x^18 + 99*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 49*x^9 + 64*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 74*x^3 + 96*x^2 + 25*x + 64, x^29 + 106*x^27 + 32*x^26 + 19*x^25 + 32*x^24 + 36*x^23 + 57*x^21 + 86*x^19 + 32*x^18 + 99*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 113*x^9 + 96*x^8 + 36*x^7 + 43*x^5 + 10*x^3 + 96*x^2 + 25*x + 96, x^29 + 106*x^27 + 99*x^25 + 80*x^24 + 36*x^23 + 25*x^21 + 96*x^20 + 86*x^19 + 83*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 33*x^9 + 48*x^8 + 36*x^7 + 11*x^5 + 96*x^4 + 10*x^3 + 41*x + 16, x^29 + 106*x^27 + 40*x^26 + 35*x^25 + 120*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 120*x^18 + 83*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 97*x^9 + 72*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 72*x^2 + 41*x + 24, x^29 + 106*x^27 + 64*x^26 + 67*x^25 + 48*x^24 + 36*x^23 + 89*x^21 + 32*x^20 + 86*x^19 + 64*x^18 + 115*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 65*x^9 + 80*x^8 + 36*x^7 + 75*x^5 + 32*x^4 + 10*x^3 + 64*x^2 + 9*x + 112, x^29 + 106*x^27 + 112*x^26 + 19*x^25 + 112*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 16*x^18 + 99*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 113*x^9 + 16*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 112*x^2 + 25*x + 112, x^29 + 106*x^27 + 16*x^26 + 67*x^25 + 96*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 48*x^18 + 115*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 65*x^9 + 32*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 80*x^2 + 9*x + 96, x^29 + 106*x^27 + 12*x^26 + 43*x^25 + 12*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 100*x^18 + 75*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 89*x^9 + 84*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 124*x^2 + 49*x + 92, x^29 + 106*x^27 + 52*x^26 + 11*x^25 + 84*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 28*x^18 + 43*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 121*x^9 + 76*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 4*x^2 + 81*x + 68, x^29 + 106*x^27 + 80*x^26 + 83*x^25 + 112*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 112*x^18 + 99*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 49*x^9 + 16*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 16*x^2 + 25*x + 48, x^29 + 106*x^27 + 88*x^26 + 51*x^25 + 120*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 72*x^18 + 3*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 81*x^9 + 72*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 120*x^2 + 121*x + 88, x^29 + 106*x^27 + 112*x^26 + 35*x^25 + 96*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 22*x^19 + 16*x^18 + 83*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 97*x^9 + 32*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 74*x^3 + 112*x^2 + 41*x + 32, x^29 + 106*x^27 + 84*x^26 + 43*x^25 + 20*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 124*x^18 + 11*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 89*x^9 + 12*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 36*x^2 + 113*x + 4, x^29 + 106*x^27 + 64*x^26 + 19*x^25 + 32*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 86*x^19 + 99*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 113*x^9 + 96*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 10*x^3 + 25*x + 96, x^29 + 106*x^27 + 32*x^26 + 67*x^25 + 112*x^24 + 100*x^23 + 25*x^21 + 96*x^20 + 22*x^19 + 32*x^18 + 51*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 65*x^9 + 16*x^8 + 100*x^7 + 11*x^5 + 96*x^4 + 74*x^3 + 96*x^2 + 73*x + 112, x^29 + 106*x^27 + 68*x^26 + 75*x^25 + 4*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 12*x^18 + 43*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 57*x^9 + 28*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 20*x^2 + 81*x + 116, x^29 + 106*x^27 + 116*x^26 + 27*x^25 + 36*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 92*x^18 + 27*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 105*x^9 + 124*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 68*x^2 + 97*x + 84, x^29 + 106*x^27 + 12*x^26 + 59*x^25 + 60*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 36*x^18 + 123*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 73*x^9 + 36*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 60*x^2 + x + 12, x^29 + 106*x^27 + 24*x^26 + 99*x^25 + 104*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 8*x^18 + 83*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 33*x^9 + 88*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 56*x^2 + 41*x + 8, x^29 + 106*x^27 + 83*x^25 + 64*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 86*x^19 + 64*x^18 + 35*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 49*x^9 + 64*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 10*x^3 + 64*x^2 + 89*x, x^29 + 106*x^27 + 116*x^26 + 123*x^25 + 36*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 28*x^18 + 123*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 9*x^9 + 124*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 4*x^2 + x + 20, x^29 + 106*x^27 + 88*x^26 + 99*x^25 + 40*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 72*x^18 + 83*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 33*x^9 + 24*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 120*x^2 + 41*x + 72, x^29 + 106*x^27 + 92*x^26 + 75*x^25 + 60*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 20*x^18 + 107*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 57*x^9 + 36*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 76*x^2 + 17*x + 12, x^29 + 106*x^27 + 16*x^26 + 67*x^25 + 64*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 86*x^19 + 48*x^18 + 115*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 65*x^9 + 64*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 10*x^3 + 80*x^2 + 9*x + 64, x^29 + 106*x^27 + 112*x^26 + 115*x^25 + 16*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 16*x^18 + 3*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 17*x^9 + 112*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 112*x^2 + 121*x + 16, x^29 + 106*x^27 + 76*x^26 + 123*x^25 + 28*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 36*x^18 + 123*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 9*x^9 + 68*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 60*x^2 + x + 44, x^29 + 106*x^27 + 4*x^26 + 27*x^25 + 116*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 76*x^18 + 91*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 105*x^9 + 44*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 84*x^2 + 33*x + 36, x^29 + 106*x^27 + 60*x^26 + 75*x^25 + 60*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 116*x^18 + 43*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 57*x^9 + 36*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 108*x^2 + 81*x + 76, x^29 + 106*x^27 + 80*x^26 + 51*x^25 + 48*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 112*x^18 + 3*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 81*x^9 + 80*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 16*x^2 + 121*x + 112, x^29 + 106*x^27 + 68*x^26 + 91*x^25 + 52*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 12*x^18 + 27*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 41*x^9 + 108*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 20*x^2 + 97*x + 100, x^29 + 106*x^27 + 60*x^26 + 107*x^25 + 92*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 116*x^18 + 11*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 25*x^9 + 4*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 108*x^2 + 113*x + 108, x^29 + 106*x^27 + 72*x^26 + 19*x^25 + 72*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 88*x^18 + 99*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 113*x^9 + 120*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 104*x^2 + 25*x + 40, x^29 + 106*x^27 + 83*x^25 + 32*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 86*x^19 + 64*x^18 + 35*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 49*x^9 + 96*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 10*x^3 + 64*x^2 + 89*x + 96, x^29 + 106*x^27 + 80*x^26 + 83*x^25 + 48*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 112*x^18 + 99*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 49*x^9 + 80*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 16*x^2 + 25*x + 112, x^29 + 106*x^27 + 96*x^26 + 83*x^25 + 36*x^23 + 57*x^21 + 64*x^20 + 86*x^19 + 96*x^18 + 35*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 49*x^9 + 36*x^7 + 43*x^5 + 64*x^4 + 10*x^3 + 32*x^2 + 89*x + 64, x^29 + 106*x^27 + 16*x^26 + 115*x^25 + 112*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 48*x^18 + 67*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 17*x^9 + 16*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 80*x^2 + 57*x + 48, x^29 + 106*x^27 + 88*x^26 + 51*x^25 + 88*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 72*x^18 + 3*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 81*x^9 + 104*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 120*x^2 + 121*x + 56, x^29 + 106*x^27 + 72*x^26 + 51*x^25 + 8*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 88*x^18 + 67*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 81*x^9 + 56*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 104*x^2 + 57*x + 104, x^29 + 106*x^27 + 116*x^26 + 59*x^25 + 100*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 28*x^18 + 59*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 73*x^9 + 60*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 4*x^2 + 65*x + 84, x^29 + 106*x^27 + 56*x^26 + 83*x^25 + 88*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 104*x^18 + 99*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 49*x^9 + 104*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 88*x^2 + 25*x + 56, x^29 + 106*x^27 + 100*x^26 + 107*x^25 + 36*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 44*x^18 + 75*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 25*x^9 + 124*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 116*x^2 + 49*x + 84, x^29 + 106*x^27 + 124*x^26 + 43*x^25 + 60*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 52*x^18 + 75*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 89*x^9 + 36*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 44*x^2 + 49*x + 76, x^29 + 106*x^27 + 28*x^26 + 11*x^25 + 60*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 20*x^18 + 107*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 121*x^9 + 36*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 76*x^2 + 17*x + 76, x^29 + 106*x^27 + 124*x^26 + 27*x^25 + 76*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 52*x^18 + 91*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 105*x^9 + 20*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 44*x^2 + 33*x + 28, x^29 + 106*x^27 + 52*x^26 + 11*x^25 + 20*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 28*x^18 + 43*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 121*x^9 + 12*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 4*x^2 + 81*x + 4, x^29 + 106*x^27 + 116*x^26 + 43*x^25 + 116*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 28*x^18 + 75*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 89*x^9 + 44*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 4*x^2 + 49*x + 36, x^29 + 106*x^27 + 92*x^26 + 27*x^25 + 12*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 84*x^18 + 91*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 105*x^9 + 84*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 12*x^2 + 33*x + 92, x^29 + 106*x^27 + 84*x^26 + 43*x^25 + 84*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 60*x^18 + 75*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 89*x^9 + 76*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 100*x^2 + 49*x + 4, x^29 + 106*x^27 + 84*x^26 + 59*x^25 + 4*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 124*x^18 + 123*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 73*x^9 + 28*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 36*x^2 + x + 52, x^29 + 106*x^27 + 76*x^26 + 75*x^25 + 44*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 36*x^18 + 43*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 57*x^9 + 52*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 60*x^2 + 81*x + 124, x^29 + 106*x^27 + 36*x^26 + 11*x^25 + 100*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 108*x^18 + 43*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 121*x^9 + 60*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 52*x^2 + 81*x + 20, x^29 + 106*x^27 + 52*x^26 + 27*x^25 + 36*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 28*x^18 + 27*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 105*x^9 + 124*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 4*x^2 + 97*x + 84, x^29 + 106*x^27 + 20*x^26 + 27*x^25 + 4*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 60*x^18 + 27*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 105*x^9 + 28*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 100*x^2 + 97*x + 52, x^29 + 106*x^27 + 48*x^26 + 51*x^25 + 80*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 16*x^18 + 3*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 81*x^9 + 48*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 112*x^2 + 121*x + 16, x^29 + 106*x^27 + 28*x^26 + 91*x^25 + 76*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 84*x^18 + 91*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 41*x^9 + 20*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 12*x^2 + 33*x + 92, x^29 + 106*x^27 + 88*x^26 + 67*x^25 + 8*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 8*x^18 + 51*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 65*x^9 + 56*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 56*x^2 + 73*x + 104, x^29 + 106*x^27 + 92*x^26 + 123*x^25 + 44*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 84*x^18 + 123*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 9*x^9 + 52*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 12*x^2 + x + 124, x^29 + 106*x^27 + 4*x^26 + 11*x^25 + 36*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 12*x^18 + 43*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 121*x^9 + 124*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 20*x^2 + 81*x + 84, x^29 + 106*x^27 + 108*x^26 + 107*x^25 + 108*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 4*x^18 + 11*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 25*x^9 + 116*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 92*x^2 + 113*x + 60, x^29 + 106*x^27 + 8*x^26 + 19*x^25 + 8*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 88*x^18 + 35*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 113*x^9 + 56*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 104*x^2 + 89*x + 40, x^29 + 106*x^27 + 40*x^26 + 67*x^25 + 88*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 56*x^18 + 115*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 65*x^9 + 104*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 8*x^2 + 9*x + 56, x^29 + 106*x^27 + 124*x^26 + 11*x^25 + 92*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 52*x^18 + 107*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 121*x^9 + 4*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 44*x^2 + 17*x + 108, x^29 + 106*x^27 + 52*x^26 + 59*x^25 + 68*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 28*x^18 + 123*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 73*x^9 + 92*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 4*x^2 + x + 116, x^29 + 106*x^27 + 76*x^26 + 91*x^25 + 60*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 36*x^18 + 27*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 41*x^9 + 36*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 60*x^2 + 97*x + 76, x^29 + 106*x^27 + 52*x^26 + 75*x^25 + 52*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 92*x^18 + 43*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 57*x^9 + 108*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 68*x^2 + 81*x + 100, x^29 + 106*x^27 + 108*x^26 + 27*x^25 + 124*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 4*x^18 + 91*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 105*x^9 + 100*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 92*x^2 + 33*x + 12, x^29 + 106*x^27 + 40*x^26 + 19*x^25 + 104*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 120*x^18 + 99*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 113*x^9 + 88*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 72*x^2 + 25*x + 72, x^29 + 106*x^27 + 68*x^26 + 107*x^25 + 36*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 76*x^18 + 75*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 25*x^9 + 124*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 84*x^2 + 49*x + 84, x^29 + 106*x^27 + 72*x^26 + 115*x^25 + 72*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 88*x^18 + 3*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 17*x^9 + 120*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 104*x^2 + 121*x + 40, x^29 + 106*x^27 + 44*x^26 + 91*x^25 + 60*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 4*x^18 + 91*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 41*x^9 + 36*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 92*x^2 + 33*x + 12, x^29 + 106*x^27 + 116*x^26 + 75*x^25 + 20*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 28*x^18 + 43*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 57*x^9 + 12*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 4*x^2 + 81*x + 68, x^29 + 106*x^27 + 16*x^26 + 51*x^25 + 16*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 48*x^18 + 3*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 81*x^9 + 112*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 80*x^2 + 121*x + 80, x^29 + 106*x^27 + 76*x^26 + 11*x^25 + 108*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 36*x^18 + 107*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 121*x^9 + 116*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 60*x^2 + 17*x + 60, x^29 + 106*x^27 + 56*x^26 + 83*x^25 + 56*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 104*x^18 + 99*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 49*x^9 + 8*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 88*x^2 + 25*x + 24, x^29 + 106*x^27 + 4*x^26 + 27*x^25 + 52*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 76*x^18 + 91*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 105*x^9 + 108*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 84*x^2 + 33*x + 100, x^29 + 106*x^27 + 40*x^26 + 67*x^25 + 56*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 120*x^18 + 51*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 65*x^9 + 8*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 72*x^2 + 73*x + 88, x^29 + 106*x^27 + 116*x^26 + 59*x^25 + 36*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 92*x^18 + 123*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 73*x^9 + 124*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 68*x^2 + x + 84, x^29 + 106*x^27 + 92*x^26 + 59*x^25 + 44*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 84*x^18 + 59*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 73*x^9 + 52*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 12*x^2 + 65*x + 124, x^29 + 106*x^27 + 60*x^26 + 11*x^25 + 28*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 116*x^18 + 107*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 121*x^9 + 68*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 108*x^2 + 17*x + 44, x^29 + 106*x^27 + 84*x^26 + 59*x^25 + 68*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 60*x^18 + 59*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 73*x^9 + 92*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 100*x^2 + 65*x + 52, x^29 + 106*x^27 + 16*x^26 + 35*x^25 + 64*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 112*x^18 + 83*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 97*x^9 + 64*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 16*x^2 + 41*x, x^29 + 106*x^27 + 4*x^26 + 75*x^25 + 4*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 12*x^18 + 107*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 57*x^9 + 28*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 20*x^2 + 17*x + 52, x^29 + 106*x^27 + 20*x^26 + 75*x^25 + 116*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 60*x^18 + 107*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 57*x^9 + 44*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 100*x^2 + 17*x + 100, x^29 + 106*x^27 + 28*x^26 + 27*x^25 + 44*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 84*x^18 + 27*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 105*x^9 + 52*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 12*x^2 + 97*x + 60, x^29 + 106*x^27 + 16*x^26 + 51*x^25 + 112*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 48*x^18 + 3*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 81*x^9 + 16*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 80*x^2 + 121*x + 48, x^29 + 106*x^27 + 72*x^26 + 83*x^25 + 104*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 24*x^18 + 99*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 49*x^9 + 88*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 40*x^2 + 25*x + 8, x^29 + 106*x^27 + 100*x^26 + 59*x^25 + 84*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 44*x^18 + 123*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 73*x^9 + 76*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 116*x^2 + x + 68, x^29 + 106*x^27 + 80*x^26 + 19*x^25 + 48*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 112*x^18 + 35*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 113*x^9 + 80*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 16*x^2 + 89*x + 112, x^29 + 106*x^27 + 72*x^26 + 115*x^25 + 40*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 88*x^18 + 3*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 17*x^9 + 24*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 104*x^2 + 121*x + 8, x^29 + 106*x^27 + 52*x^26 + 75*x^25 + 84*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 92*x^18 + 43*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 57*x^9 + 76*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 68*x^2 + 81*x + 4, x^29 + 106*x^27 + 116*x^26 + 27*x^25 + 36*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 28*x^18 + 91*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 105*x^9 + 124*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 4*x^2 + 33*x + 20, x^29 + 106*x^27 + 96*x^26 + 3*x^25 + 48*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 32*x^20 + 86*x^19 + 32*x^18 + 51*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + x^9 + 80*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 32*x^4 + 10*x^3 + 96*x^2 + 73*x + 112, x^29 + 106*x^27 + 32*x^26 + 67*x^25 + 16*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 86*x^19 + 96*x^18 + 115*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 65*x^9 + 112*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 10*x^3 + 32*x^2 + 9*x + 80, x^29 + 106*x^27 + 24*x^26 + 51*x^25 + 120*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 72*x^18 + 67*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 81*x^9 + 72*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 120*x^2 + 57*x + 24, x^29 + 106*x^27 + 40*x^26 + 51*x^25 + 72*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 56*x^18 + 3*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 81*x^9 + 120*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 8*x^2 + 121*x + 104, x^29 + 106*x^27 + 40*x^26 + 19*x^25 + 40*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 56*x^18 + 35*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 113*x^9 + 24*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 8*x^2 + 89*x + 72, x^29 + 106*x^27 + 64*x^26 + 35*x^25 + 48*x^24 + 36*x^23 + 25*x^21 + 32*x^20 + 86*x^19 + 64*x^18 + 19*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 97*x^9 + 80*x^8 + 36*x^7 + 11*x^5 + 32*x^4 + 10*x^3 + 64*x^2 + 105*x + 112, x^29 + 106*x^27 + 108*x^26 + 27*x^25 + 92*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 68*x^18 + 27*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 105*x^9 + 4*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 28*x^2 + 97*x + 44, x^29 + 106*x^27 + 80*x^26 + 35*x^25 + 32*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 22*x^19 + 48*x^18 + 83*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 97*x^9 + 96*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 74*x^3 + 80*x^2 + 41*x + 96, x^29 + 106*x^27 + 48*x^26 + 19*x^25 + 80*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 16*x^18 + 35*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 113*x^9 + 48*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 112*x^2 + 89*x + 16, x^29 + 106*x^27 + 24*x^26 + 99*x^25 + 8*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 72*x^18 + 19*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 33*x^9 + 56*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 120*x^2 + 105*x + 104, x^29 + 106*x^27 + 16*x^26 + 51*x^25 + 16*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 112*x^18 + 67*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 81*x^9 + 112*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 16*x^2 + 57*x + 16, x^29 + 106*x^27 + 12*x^26 + 27*x^25 + 92*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 36*x^18 + 27*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 105*x^9 + 4*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 60*x^2 + 97*x + 44, x^29 + 106*x^27 + 52*x^26 + 91*x^25 + 4*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 92*x^18 + 27*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 41*x^9 + 28*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 68*x^2 + 97*x + 116, x^29 + 106*x^27 + 108*x^26 + 75*x^25 + 108*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 68*x^18 + 107*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 57*x^9 + 116*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 28*x^2 + 17*x + 124, x^29 + 106*x^27 + 104*x^26 + 35*x^25 + 56*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 56*x^18 + 83*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 97*x^9 + 8*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 8*x^2 + 41*x + 88, x^29 + 106*x^27 + 56*x^26 + 115*x^25 + 88*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 40*x^18 + 3*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 17*x^9 + 104*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 24*x^2 + 121*x + 120, x^29 + 106*x^27 + 16*x^26 + 67*x^25 + 32*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 48*x^18 + 115*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 65*x^9 + 96*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 80*x^2 + 9*x + 32, x^29 + 106*x^27 + 44*x^26 + 123*x^25 + 28*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 4*x^18 + 59*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 9*x^9 + 68*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 92*x^2 + 65*x + 108, x^29 + 106*x^27 + 96*x^26 + 51*x^25 + 96*x^24 + 36*x^23 + 121*x^21 + 86*x^19 + 96*x^18 + 67*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 81*x^9 + 32*x^8 + 36*x^7 + 107*x^5 + 10*x^3 + 32*x^2 + 57*x + 32, x^29 + 106*x^27 + 120*x^26 + 51*x^25 + 56*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 40*x^18 + 3*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 81*x^9 + 8*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 24*x^2 + 121*x + 24, x^29 + 106*x^27 + 24*x^26 + 35*x^25 + 72*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 72*x^18 + 83*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 97*x^9 + 120*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 120*x^2 + 41*x + 40, x^29 + 106*x^27 + 112*x^26 + 99*x^25 + 32*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 80*x^18 + 83*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 33*x^9 + 96*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 48*x^2 + 41*x + 32, x^29 + 106*x^27 + 104*x^26 + 51*x^25 + 72*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 56*x^18 + 67*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 81*x^9 + 120*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 8*x^2 + 57*x + 40, x^29 + 106*x^27 + 108*x^26 + 43*x^25 + 12*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 4*x^18 + 75*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 89*x^9 + 84*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 92*x^2 + 49*x + 92, x^29 + 106*x^27 + 20*x^26 + 123*x^25 + 36*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 60*x^18 + 59*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 9*x^9 + 124*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 100*x^2 + 65*x + 84, x^29 + 106*x^27 + 16*x^26 + 99*x^25 + 64*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 112*x^18 + 19*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 33*x^9 + 64*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 16*x^2 + 105*x, x^29 + 106*x^27 + 72*x^26 + 35*x^25 + 56*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 88*x^18 + 83*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 97*x^9 + 8*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 104*x^2 + 41*x + 88, x^29 + 106*x^27 + 36*x^26 + 59*x^25 + 20*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 44*x^18 + 59*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 73*x^9 + 12*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 116*x^2 + 65*x + 68, x^29 + 106*x^27 + 48*x^26 + 3*x^25 + 36*x^23 + 32*x^22 + 89*x^21 + 86*x^19 + 16*x^18 + 51*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + x^9 + 36*x^7 + 32*x^6 + 75*x^5 + 10*x^3 + 112*x^2 + 73*x, x^29 + 106*x^27 + 104*x^26 + 51*x^25 + 8*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 56*x^18 + 67*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 81*x^9 + 56*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 8*x^2 + 57*x + 104, x^29 + 106*x^27 + 96*x^26 + 99*x^25 + 112*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 86*x^19 + 32*x^18 + 83*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 33*x^9 + 16*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 10*x^3 + 96*x^2 + 41*x + 48, x^29 + 106*x^27 + 48*x^26 + 115*x^25 + 16*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 16*x^18 + 67*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 17*x^9 + 112*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 112*x^2 + 57*x + 80, x^29 + 106*x^27 + 80*x^26 + 51*x^25 + 112*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 48*x^18 + 67*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 81*x^9 + 16*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 80*x^2 + 57*x + 112, x^29 + 106*x^27 + 84*x^26 + 123*x^25 + 100*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 60*x^18 + 123*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 9*x^9 + 60*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 100*x^2 + x + 84, x^29 + 106*x^27 + 64*x^26 + 35*x^25 + 112*x^24 + 36*x^23 + 25*x^21 + 32*x^20 + 86*x^19 + 64*x^18 + 19*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 97*x^9 + 16*x^8 + 36*x^7 + 11*x^5 + 32*x^4 + 10*x^3 + 64*x^2 + 105*x + 48, x^29 + 106*x^27 + 4*x^26 + 107*x^25 + 36*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 76*x^18 + 11*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 25*x^9 + 124*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 84*x^2 + 113*x + 20, x^29 + 106*x^27 + 112*x^26 + 99*x^25 + 36*x^23 + 32*x^22 + 25*x^21 + 86*x^19 + 80*x^18 + 83*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 33*x^9 + 36*x^7 + 32*x^6 + 11*x^5 + 10*x^3 + 48*x^2 + 41*x, x^29 + 106*x^27 + 76*x^26 + 43*x^25 + 12*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 100*x^18 + 11*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 89*x^9 + 84*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 124*x^2 + 113*x + 28, x^29 + 106*x^27 + 80*x^26 + 19*x^25 + 80*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 112*x^18 + 35*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 113*x^9 + 48*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 16*x^2 + 89*x + 16, x^29 + 106*x^27 + 104*x^26 + 51*x^25 + 40*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 120*x^18 + 3*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 81*x^9 + 24*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 72*x^2 + 121*x + 72, x^29 + 106*x^27 + 116*x^26 + 43*x^25 + 52*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 92*x^18 + 11*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 89*x^9 + 108*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 68*x^2 + 113*x + 36, x^29 + 106*x^27 + 88*x^26 + 19*x^25 + 88*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 8*x^18 + 99*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 113*x^9 + 104*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 56*x^2 + 25*x + 120, x^29 + 106*x^27 + 104*x^26 + 51*x^25 + 40*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 56*x^18 + 67*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 81*x^9 + 24*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 8*x^2 + 57*x + 8, x^29 + 106*x^27 + 68*x^26 + 91*x^25 + 116*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 76*x^18 + 91*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 41*x^9 + 44*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 84*x^2 + 33*x + 100, x^29 + 106*x^27 + 12*x^26 + 59*x^25 + 28*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 36*x^18 + 123*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 73*x^9 + 68*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 60*x^2 + x + 108, x^29 + 106*x^27 + 92*x^26 + 107*x^25 + 28*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 84*x^18 + 11*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 25*x^9 + 68*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 12*x^2 + 113*x + 44, x^29 + 106*x^27 + 68*x^26 + 123*x^25 + 20*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 12*x^18 + 123*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 9*x^9 + 12*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 20*x^2 + x + 68, x^29 + 106*x^27 + 24*x^26 + 115*x^25 + 56*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 8*x^18 + 67*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 17*x^9 + 8*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 56*x^2 + 57*x + 24, x^29 + 106*x^27 + 52*x^26 + 27*x^25 + 100*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 92*x^18 + 91*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 105*x^9 + 60*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 68*x^2 + 33*x + 84, x^29 + 106*x^27 + 84*x^26 + 91*x^25 + 68*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 60*x^18 + 27*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 41*x^9 + 92*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 100*x^2 + 97*x + 52, x^29 + 106*x^27 + 60*x^26 + 91*x^25 + 108*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 116*x^18 + 27*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 41*x^9 + 116*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 108*x^2 + 97*x + 60, x^29 + 106*x^27 + 64*x^26 + 3*x^25 + 80*x^24 + 36*x^23 + 89*x^21 + 96*x^20 + 86*x^19 + 64*x^18 + 51*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + x^9 + 48*x^8 + 36*x^7 + 75*x^5 + 96*x^4 + 10*x^3 + 64*x^2 + 73*x + 16, x^29 + 106*x^27 + 112*x^26 + 51*x^25 + 112*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 16*x^18 + 67*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 81*x^9 + 16*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 112*x^2 + 57*x + 112, x^29 + 106*x^27 + 36*x^26 + 43*x^25 + 36*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 44*x^18 + 75*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 89*x^9 + 124*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 116*x^2 + 49*x + 20, x^29 + 106*x^27 + 100*x^26 + 43*x^25 + 4*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 108*x^18 + 75*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 89*x^9 + 28*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 52*x^2 + 49*x + 116, x^29 + 106*x^27 + 112*x^26 + 83*x^25 + 48*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 80*x^18 + 99*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 49*x^9 + 80*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 48*x^2 + 25*x + 112, x^29 + 106*x^27 + 88*x^26 + 115*x^25 + 24*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 8*x^18 + 3*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 17*x^9 + 40*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 56*x^2 + 121*x + 56, x^29 + 106*x^27 + 24*x^26 + 3*x^25 + 104*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 72*x^18 + 115*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + x^9 + 88*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 120*x^2 + 9*x + 72, x^29 + 106*x^27 + 108*x^26 + 91*x^25 + 124*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 4*x^18 + 27*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 41*x^9 + 100*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 92*x^2 + 97*x + 12, x^29 + 106*x^27 + 44*x^26 + 11*x^25 + 44*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 4*x^18 + 43*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 121*x^9 + 52*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 92*x^2 + 81*x + 60, x^29 + 106*x^27 + 52*x^26 + 59*x^25 + 100*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 28*x^18 + 123*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 73*x^9 + 60*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 4*x^2 + x + 20, x^29 + 106*x^27 + 120*x^26 + 19*x^25 + 120*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 104*x^18 + 99*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 113*x^9 + 72*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 88*x^2 + 25*x + 24, x^29 + 106*x^27 + 92*x^26 + 91*x^25 + 108*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 20*x^18 + 91*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 41*x^9 + 116*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 76*x^2 + 33*x + 124, x^29 + 106*x^27 + 28*x^26 + 11*x^25 + 28*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 84*x^18 + 43*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 121*x^9 + 68*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 12*x^2 + 81*x + 108, x^29 + 106*x^27 + 28*x^26 + 91*x^25 + 76*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 20*x^18 + 27*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 41*x^9 + 20*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 76*x^2 + 97*x + 28, x^29 + 106*x^27 + 68*x^26 + 123*x^25 + 52*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 12*x^18 + 123*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 9*x^9 + 108*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 20*x^2 + x + 100, x^29 + 106*x^27 + 124*x^26 + 27*x^25 + 76*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 116*x^18 + 27*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 105*x^9 + 20*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 108*x^2 + 97*x + 92, x^29 + 106*x^27 + 104*x^26 + 35*x^25 + 120*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 56*x^18 + 83*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 97*x^9 + 72*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 8*x^2 + 41*x + 24, x^29 + 106*x^27 + 84*x^26 + 11*x^25 + 20*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 124*x^18 + 43*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 121*x^9 + 12*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 36*x^2 + 81*x + 4, x^29 + 106*x^27 + 3*x^25 + 112*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 22*x^19 + 64*x^18 + 115*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + x^9 + 16*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 74*x^3 + 64*x^2 + 9*x + 112, x^29 + 106*x^27 + 48*x^26 + 51*x^25 + 112*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 16*x^18 + 3*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 81*x^9 + 16*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 112*x^2 + 121*x + 48, x^29 + 106*x^27 + 8*x^26 + 83*x^25 + 40*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 24*x^18 + 35*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 49*x^9 + 24*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 40*x^2 + 89*x + 8, x^29 + 106*x^27 + 36*x^26 + 75*x^25 + 68*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 44*x^18 + 43*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 57*x^9 + 92*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 116*x^2 + 81*x + 52, x^29 + 106*x^27 + 68*x^26 + 59*x^25 + 84*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 12*x^18 + 59*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 73*x^9 + 76*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 20*x^2 + 65*x + 4, x^29 + 106*x^27 + 96*x^26 + 115*x^25 + 64*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 22*x^19 + 32*x^18 + 67*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 17*x^9 + 64*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 74*x^3 + 96*x^2 + 57*x + 64, x^29 + 106*x^27 + 76*x^26 + 27*x^25 + 28*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 36*x^18 + 91*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 105*x^9 + 68*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 60*x^2 + 33*x + 44, x^29 + 106*x^27 + 44*x^26 + 43*x^25 + 44*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 4*x^18 + 11*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 89*x^9 + 52*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 92*x^2 + 113*x + 60, x^29 + 106*x^27 + 40*x^26 + 19*x^25 + 72*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 56*x^18 + 35*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 113*x^9 + 120*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 8*x^2 + 89*x + 104, x^29 + 106*x^27 + 88*x^26 + 67*x^25 + 72*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 8*x^18 + 51*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 65*x^9 + 120*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 56*x^2 + 73*x + 40, x^29 + 106*x^27 + 124*x^26 + 107*x^25 + 124*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 116*x^18 + 75*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 25*x^9 + 100*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 108*x^2 + 49*x + 76, x^29 + 106*x^27 + 56*x^26 + 67*x^25 + 8*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 40*x^18 + 51*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 65*x^9 + 56*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 24*x^2 + 73*x + 104, x^29 + 106*x^27 + 96*x^26 + 83*x^25 + 96*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 22*x^19 + 32*x^18 + 99*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 49*x^9 + 32*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 74*x^3 + 96*x^2 + 25*x + 96, x^29 + 106*x^27 + 48*x^26 + 115*x^25 + 16*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 80*x^18 + 3*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 17*x^9 + 112*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 48*x^2 + 121*x + 16, x^29 + 106*x^27 + 48*x^26 + 51*x^25 + 48*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 80*x^18 + 67*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 81*x^9 + 80*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 48*x^2 + 57*x + 48, x^29 + 106*x^27 + 60*x^26 + 91*x^25 + 108*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 52*x^18 + 91*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 41*x^9 + 116*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 44*x^2 + 33*x + 124, x^29 + 106*x^27 + 20*x^26 + 11*x^25 + 84*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 124*x^18 + 107*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 121*x^9 + 76*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 36*x^2 + 17*x + 4, x^29 + 106*x^27 + 32*x^26 + 51*x^25 + 96*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 22*x^19 + 96*x^18 + 3*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 81*x^9 + 32*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 74*x^3 + 32*x^2 + 121*x + 96, x^29 + 106*x^27 + 104*x^26 + 115*x^25 + 72*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 56*x^18 + 3*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 17*x^9 + 120*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 8*x^2 + 121*x + 40, x^29 + 106*x^27 + 44*x^26 + 75*x^25 + 108*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 4*x^18 + 107*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 57*x^9 + 116*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 92*x^2 + 17*x + 124, x^29 + 106*x^27 + 32*x^26 + 35*x^25 + 16*x^24 + 100*x^23 + 89*x^21 + 32*x^20 + 22*x^19 + 32*x^18 + 83*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 97*x^9 + 112*x^8 + 100*x^7 + 75*x^5 + 32*x^4 + 74*x^3 + 96*x^2 + 41*x + 16, x^29 + 106*x^27 + 56*x^26 + 83*x^25 + 120*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 104*x^18 + 99*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 49*x^9 + 72*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 88*x^2 + 25*x + 88, x^29 + 106*x^27 + 8*x^26 + 51*x^25 + 40*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 88*x^18 + 3*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 81*x^9 + 24*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 104*x^2 + 121*x + 72, x^29 + 106*x^27 + 120*x^26 + 51*x^25 + 88*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 40*x^18 + 3*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 81*x^9 + 104*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 24*x^2 + 121*x + 56, x^29 + 106*x^27 + 80*x^26 + 99*x^25 + 64*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 86*x^19 + 112*x^18 + 83*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 33*x^9 + 64*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 10*x^3 + 16*x^2 + 41*x + 64, x^29 + 106*x^27 + 68*x^26 + 27*x^25 + 116*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 12*x^18 + 91*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 105*x^9 + 44*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 20*x^2 + 33*x + 36, x^29 + 106*x^27 + 60*x^26 + 59*x^25 + 12*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 52*x^18 + 123*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 73*x^9 + 84*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 44*x^2 + x + 28, x^29 + 106*x^27 + 88*x^26 + 67*x^25 + 40*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 8*x^18 + 51*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 65*x^9 + 24*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 56*x^2 + 73*x + 8, x^29 + 106*x^27 + 120*x^26 + 35*x^25 + 8*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 40*x^18 + 19*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 97*x^9 + 56*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 24*x^2 + 105*x + 40, x^29 + 106*x^27 + 80*x^26 + 67*x^25 + 96*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 112*x^18 + 115*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 65*x^9 + 32*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 16*x^2 + 9*x + 96, x^29 + 106*x^27 + 116*x^26 + 107*x^25 + 52*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 92*x^18 + 75*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 25*x^9 + 108*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 68*x^2 + 49*x + 36, x^29 + 106*x^27 + 76*x^26 + 43*x^25 + 76*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 36*x^18 + 75*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 89*x^9 + 20*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 60*x^2 + 49*x + 28, x^29 + 106*x^27 + 92*x^26 + 91*x^25 + 44*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 84*x^18 + 27*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 41*x^9 + 52*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 12*x^2 + 97*x + 124, x^29 + 106*x^27 + 108*x^26 + 59*x^25 + 92*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 4*x^18 + 59*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 73*x^9 + 4*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 92*x^2 + 65*x + 108, x^29 + 106*x^27 + 16*x^26 + 3*x^25 + 32*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 48*x^18 + 51*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + x^9 + 96*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 80*x^2 + 73*x + 32, x^29 + 106*x^27 + 100*x^26 + 59*x^25 + 52*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 44*x^18 + 123*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 73*x^9 + 108*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 116*x^2 + x + 36, x^29 + 106*x^27 + 72*x^26 + 83*x^25 + 8*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 24*x^18 + 99*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 49*x^9 + 56*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 40*x^2 + 25*x + 40, x^29 + 106*x^27 + 80*x^26 + 67*x^25 + 32*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 112*x^18 + 115*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 65*x^9 + 96*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 16*x^2 + 9*x + 32, x^29 + 106*x^27 + 80*x^26 + 115*x^25 + 48*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 112*x^18 + 67*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 17*x^9 + 80*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 16*x^2 + 57*x + 112, x^29 + 106*x^27 + 116*x^26 + 59*x^25 + 100*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 92*x^18 + 123*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 73*x^9 + 60*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 68*x^2 + x + 20, x^29 + 106*x^27 + 80*x^26 + 67*x^25 + 64*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 48*x^18 + 51*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 65*x^9 + 64*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 80*x^2 + 73*x, x^29 + 106*x^27 + 80*x^26 + 115*x^25 + 48*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 48*x^18 + 3*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 17*x^9 + 80*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 80*x^2 + 121*x + 48, x^29 + 106*x^27 + 68*x^26 + 27*x^25 + 84*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 76*x^18 + 27*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 105*x^9 + 76*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 84*x^2 + 97*x + 68, x^29 + 106*x^27 + 60*x^26 + 11*x^25 + 60*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 116*x^18 + 107*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 121*x^9 + 36*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 108*x^2 + 17*x + 76, x^29 + 106*x^27 + 4*x^26 + 59*x^25 + 20*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 12*x^18 + 123*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 73*x^9 + 12*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 20*x^2 + x + 4, x^29 + 106*x^27 + 104*x^26 + 19*x^25 + 40*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 120*x^18 + 35*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 113*x^9 + 24*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 72*x^2 + 89*x + 72, x^29 + 106*x^27 + 88*x^26 + 3*x^25 + 104*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 8*x^18 + 115*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + x^9 + 88*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 56*x^2 + 9*x + 72, x^29 + 106*x^27 + 100*x^26 + 123*x^25 + 84*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 108*x^18 + 123*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 9*x^9 + 76*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 52*x^2 + x + 4, x^29 + 106*x^27 + 36*x^26 + 107*x^25 + 36*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 108*x^18 + 75*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 25*x^9 + 124*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 52*x^2 + 49*x + 84, x^29 + 106*x^27 + 36*x^26 + 11*x^25 + 36*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 108*x^18 + 43*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 121*x^9 + 124*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 52*x^2 + 81*x + 84, x^29 + 106*x^27 + 4*x^26 + 59*x^25 + 52*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 12*x^18 + 123*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 73*x^9 + 108*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 20*x^2 + x + 36, x^29 + 106*x^27 + 20*x^26 + 27*x^25 + 68*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 60*x^18 + 27*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 105*x^9 + 92*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 100*x^2 + 97*x + 116, x^29 + 106*x^27 + 76*x^26 + 107*x^25 + 76*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 36*x^18 + 11*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 25*x^9 + 20*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 60*x^2 + 113*x + 28, x^29 + 106*x^27 + 116*x^26 + 11*x^25 + 116*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 28*x^18 + 107*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 121*x^9 + 44*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 4*x^2 + 17*x + 36, x^29 + 106*x^27 + 96*x^26 + 83*x^25 + 100*x^23 + 64*x^22 + 121*x^21 + 22*x^19 + 32*x^18 + 99*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 49*x^9 + 100*x^7 + 64*x^6 + 107*x^5 + 74*x^3 + 96*x^2 + 25*x, x^29 + 106*x^27 + 24*x^26 + 99*x^25 + 72*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 72*x^18 + 19*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 33*x^9 + 120*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 120*x^2 + 105*x + 40, x^29 + 106*x^27 + 16*x^26 + 115*x^25 + 112*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 112*x^18 + 3*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 17*x^9 + 16*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 16*x^2 + 121*x + 112, x^29 + 106*x^27 + 88*x^26 + 35*x^25 + 104*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 72*x^18 + 19*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 97*x^9 + 88*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 120*x^2 + 105*x + 8, x^29 + 106*x^27 + 84*x^26 + 11*x^25 + 84*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 124*x^18 + 43*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 121*x^9 + 76*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 36*x^2 + 81*x + 68, x^29 + 106*x^27 + 28*x^26 + 123*x^25 + 44*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 20*x^18 + 123*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 9*x^9 + 52*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 76*x^2 + x + 124, x^29 + 106*x^27 + 48*x^26 + 35*x^25 + 96*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 22*x^19 + 80*x^18 + 83*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 97*x^9 + 32*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 74*x^3 + 48*x^2 + 41*x + 32, x^29 + 106*x^27 + 4*x^26 + 43*x^25 + 68*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 76*x^18 + 75*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 89*x^9 + 92*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 84*x^2 + 49*x + 52, x^29 + 106*x^27 + 76*x^26 + 75*x^25 + 12*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 100*x^18 + 107*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 57*x^9 + 84*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 124*x^2 + 17*x + 28, x^29 + 106*x^27 + 104*x^26 + 115*x^25 + 104*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 120*x^18 + 67*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 17*x^9 + 88*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 72*x^2 + 57*x + 8, x^29 + 106*x^27 + 92*x^26 + 27*x^25 + 108*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 84*x^18 + 91*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 105*x^9 + 116*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 12*x^2 + 33*x + 60, x^29 + 106*x^27 + 80*x^26 + 67*x^25 + 100*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 48*x^18 + 51*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 65*x^9 + 100*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 80*x^2 + 73*x + 64, x^29 + 106*x^27 + 4*x^26 + 107*x^25 + 4*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 12*x^18 + 75*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 25*x^9 + 28*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 20*x^2 + 49*x + 52, x^29 + 106*x^27 + 88*x^26 + 83*x^25 + 56*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 72*x^18 + 99*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 49*x^9 + 8*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 120*x^2 + 25*x + 24, x^29 + 106*x^27 + 32*x^26 + 83*x^25 + 100*x^23 + 64*x^22 + 121*x^21 + 22*x^19 + 96*x^18 + 99*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 49*x^9 + 100*x^7 + 64*x^6 + 107*x^5 + 74*x^3 + 32*x^2 + 25*x, x^29 + 106*x^27 + 52*x^26 + 11*x^25 + 20*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 92*x^18 + 107*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 121*x^9 + 12*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 68*x^2 + 17*x + 68, x^29 + 106*x^27 + 52*x^26 + 43*x^25 + 52*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 28*x^18 + 11*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 89*x^9 + 108*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 4*x^2 + 113*x + 36, x^29 + 106*x^27 + 44*x^26 + 59*x^25 + 92*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 68*x^18 + 59*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 73*x^9 + 4*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 28*x^2 + 65*x + 108, x^29 + 106*x^27 + 40*x^26 + 35*x^25 + 88*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 120*x^18 + 83*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 97*x^9 + 104*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 72*x^2 + 41*x + 120, x^29 + 106*x^27 + 124*x^26 + 75*x^25 + 28*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 116*x^18 + 107*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 57*x^9 + 68*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 108*x^2 + 17*x + 108, x^29 + 106*x^27 + 20*x^26 + 107*x^25 + 20*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 60*x^18 + 75*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 25*x^9 + 12*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 100*x^2 + 49*x + 4, x^29 + 106*x^27 + 12*x^26 + 123*x^25 + 28*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 36*x^18 + 59*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 9*x^9 + 68*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 60*x^2 + 65*x + 108, x^29 + 106*x^27 + 88*x^26 + 51*x^25 + 56*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 8*x^18 + 67*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 81*x^9 + 8*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 56*x^2 + 57*x + 88, x^29 + 106*x^27 + 120*x^26 + 3*x^25 + 40*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 40*x^18 + 51*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + x^9 + 24*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 24*x^2 + 73*x + 72, x^29 + 106*x^27 + 100*x^26 + 91*x^25 + 116*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 44*x^18 + 91*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 41*x^9 + 44*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 116*x^2 + 33*x + 100, x^29 + 106*x^27 + 96*x^26 + 67*x^25 + 48*x^24 + 100*x^23 + 25*x^21 + 96*x^20 + 22*x^19 + 96*x^18 + 51*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 65*x^9 + 80*x^8 + 100*x^7 + 11*x^5 + 96*x^4 + 74*x^3 + 32*x^2 + 73*x + 48, x^29 + 106*x^27 + 16*x^26 + 3*x^25 + 64*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 112*x^18 + 115*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + x^9 + 64*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 16*x^2 + 9*x, x^29 + 106*x^27 + 92*x^26 + 59*x^25 + 108*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 20*x^18 + 123*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 73*x^9 + 116*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 76*x^2 + x + 124, x^29 + 106*x^27 + 124*x^26 + 75*x^25 + 92*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 116*x^18 + 107*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 57*x^9 + 4*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 108*x^2 + 17*x + 44, x^29 + 106*x^27 + 72*x^26 + 67*x^25 + 88*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 24*x^18 + 115*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 65*x^9 + 104*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 40*x^2 + 9*x + 56, x^29 + 106*x^27 + 36*x^26 + 107*x^25 + 68*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 44*x^18 + 11*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 25*x^9 + 92*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 116*x^2 + 113*x + 52, x^29 + 106*x^27 + 116*x^26 + 123*x^25 + 4*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 92*x^18 + 59*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 9*x^9 + 28*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 68*x^2 + 65*x + 52, x^29 + 106*x^27 + 60*x^26 + 107*x^25 + 60*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 116*x^18 + 11*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 25*x^9 + 36*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 108*x^2 + 113*x + 76, x^29 + 106*x^27 + 40*x^26 + 67*x^25 + 24*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 120*x^18 + 51*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 65*x^9 + 40*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 72*x^2 + 73*x + 56, x^29 + 106*x^27 + 96*x^26 + 115*x^25 + 64*x^24 + 36*x^23 + 121*x^21 + 64*x^20 + 86*x^19 + 96*x^18 + 3*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 17*x^9 + 64*x^8 + 36*x^7 + 107*x^5 + 64*x^4 + 10*x^3 + 32*x^2 + 121*x, x^29 + 106*x^27 + 20*x^26 + 59*x^25 + 100*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 60*x^18 + 123*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 73*x^9 + 60*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 100*x^2 + x + 20, x^29 + 106*x^27 + 64*x^26 + 115*x^25 + 64*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 86*x^19 + 3*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 17*x^9 + 64*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 10*x^3 + 121*x, x^29 + 106*x^27 + 12*x^26 + 91*x^25 + 60*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 36*x^18 + 91*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 41*x^9 + 36*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 60*x^2 + 33*x + 12, x^29 + 106*x^27 + 48*x^26 + 35*x^25 + 64*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 86*x^19 + 16*x^18 + 19*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 97*x^9 + 64*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 10*x^3 + 112*x^2 + 105*x + 64, x^29 + 106*x^27 + 67*x^25 + 80*x^24 + 36*x^23 + 89*x^21 + 96*x^20 + 86*x^19 + 115*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 65*x^9 + 48*x^8 + 36*x^7 + 75*x^5 + 96*x^4 + 10*x^3 + 9*x + 16, x^29 + 106*x^27 + 44*x^26 + 123*x^25 + 124*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 4*x^18 + 59*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 9*x^9 + 100*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 92*x^2 + 65*x + 76, x^29 + 106*x^27 + 60*x^26 + 123*x^25 + 76*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 52*x^18 + 59*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 9*x^9 + 20*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 44*x^2 + 65*x + 92, x^29 + 106*x^27 + 104*x^26 + 99*x^25 + 24*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 56*x^18 + 19*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 33*x^9 + 40*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 8*x^2 + 105*x + 56, x^29 + 106*x^27 + 115*x^25 + 64*x^24 + 36*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 86*x^19 + 64*x^18 + 3*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 17*x^9 + 64*x^8 + 36*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 10*x^3 + 64*x^2 + 121*x, x^29 + 106*x^27 + 52*x^26 + 123*x^25 + 100*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 28*x^18 + 59*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 9*x^9 + 60*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 4*x^2 + 65*x + 20, x^29 + 106*x^27 + 108*x^26 + 27*x^25 + 28*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 68*x^18 + 27*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 105*x^9 + 68*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 28*x^2 + 97*x + 108, x^29 + 106*x^27 + 88*x^26 + 115*x^25 + 120*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 8*x^18 + 3*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 17*x^9 + 72*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 56*x^2 + 121*x + 24, x^29 + 106*x^27 + 32*x^26 + 115*x^25 + 100*x^23 + 64*x^22 + 57*x^21 + 22*x^19 + 96*x^18 + 67*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 17*x^9 + 100*x^7 + 64*x^6 + 43*x^5 + 74*x^3 + 32*x^2 + 57*x, x^29 + 106*x^27 + 68*x^26 + 27*x^25 + 20*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 76*x^18 + 27*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 105*x^9 + 12*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 84*x^2 + 97*x + 4, x^29 + 106*x^27 + 24*x^26 + 83*x^25 + 56*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 8*x^18 + 99*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 49*x^9 + 8*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 56*x^2 + 25*x + 24, x^29 + 106*x^27 + 116*x^26 + 11*x^25 + 84*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 28*x^18 + 107*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 121*x^9 + 76*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 4*x^2 + 17*x + 4, x^29 + 106*x^27 + 68*x^26 + 91*x^25 + 20*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 12*x^18 + 27*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 41*x^9 + 12*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 20*x^2 + 97*x + 68, x^29 + 106*x^27 + 120*x^26 + 19*x^25 + 88*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 40*x^18 + 35*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 113*x^9 + 104*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 24*x^2 + 89*x + 56, x^29 + 106*x^27 + 68*x^26 + 43*x^25 + 68*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 12*x^18 + 75*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 89*x^9 + 92*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 20*x^2 + 49*x + 52, x^29 + 106*x^27 + 76*x^26 + 75*x^25 + 44*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 100*x^18 + 107*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 57*x^9 + 52*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 124*x^2 + 17*x + 60, x^29 + 106*x^27 + 68*x^26 + 75*x^25 + 100*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 12*x^18 + 43*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 57*x^9 + 60*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 20*x^2 + 81*x + 84, x^29 + 106*x^27 + 12*x^26 + 11*x^25 + 44*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 100*x^18 + 107*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 121*x^9 + 52*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 124*x^2 + 17*x + 124, x^29 + 106*x^27 + 84*x^26 + 75*x^25 + 20*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 124*x^18 + 107*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 57*x^9 + 12*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 36*x^2 + 17*x + 4, x^29 + 106*x^27 + 8*x^26 + 51*x^25 + 104*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 88*x^18 + 3*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 81*x^9 + 88*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 104*x^2 + 121*x + 8, x^29 + 106*x^27 + 72*x^26 + 3*x^25 + 24*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 88*x^18 + 115*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + x^9 + 40*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 104*x^2 + 9*x + 56, x^29 + 106*x^27 + 72*x^26 + 67*x^25 + 88*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 88*x^18 + 51*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 65*x^9 + 104*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 104*x^2 + 73*x + 120, x^29 + 106*x^27 + 84*x^26 + 123*x^25 + 68*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 60*x^18 + 123*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 9*x^9 + 92*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 100*x^2 + x + 52, x^29 + 106*x^27 + 52*x^26 + 123*x^25 + 4*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 28*x^18 + 59*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 9*x^9 + 28*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 4*x^2 + 65*x + 52, x^29 + 106*x^27 + 88*x^26 + 3*x^25 + 40*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 72*x^18 + 51*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + x^9 + 24*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 120*x^2 + 73*x + 72, x^29 + 106*x^27 + 96*x^26 + 67*x^25 + 80*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 86*x^19 + 32*x^18 + 115*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 65*x^9 + 48*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 10*x^3 + 96*x^2 + 9*x + 16, x^29 + 106*x^27 + 84*x^26 + 27*x^25 + 36*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 124*x^18 + 27*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 105*x^9 + 124*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 36*x^2 + 97*x + 84, x^29 + 106*x^27 + 108*x^26 + 75*x^25 + 108*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 54*x^19 + 4*x^18 + 43*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 57*x^9 + 116*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 106*x^3 + 92*x^2 + 81*x + 60, x^29 + 106*x^27 + 72*x^26 + 19*x^25 + 40*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 24*x^18 + 35*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 113*x^9 + 24*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 40*x^2 + 89*x + 72, x^29 + 106*x^27 + 64*x^26 + 3*x^25 + 48*x^24 + 36*x^23 + 89*x^21 + 32*x^20 + 86*x^19 + 64*x^18 + 51*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + x^9 + 80*x^8 + 36*x^7 + 75*x^5 + 32*x^4 + 10*x^3 + 64*x^2 + 73*x + 112, x^29 + 106*x^27 + 76*x^26 + 27*x^25 + 92*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 100*x^18 + 27*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 105*x^9 + 4*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 124*x^2 + 97*x + 44, x^29 + 106*x^27 + 92*x^26 + 43*x^25 + 28*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 20*x^18 + 11*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 89*x^9 + 68*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 76*x^2 + 113*x + 108, x^29 + 106*x^27 + 32*x^26 + 83*x^25 + 32*x^24 + 36*x^23 + 57*x^21 + 86*x^19 + 32*x^18 + 35*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 49*x^9 + 96*x^8 + 36*x^7 + 43*x^5 + 10*x^3 + 96*x^2 + 89*x + 96, x^29 + 106*x^27 + 16*x^26 + 51*x^25 + 48*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 48*x^18 + 3*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 81*x^9 + 80*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 80*x^2 + 121*x + 112, x^29 + 106*x^27 + 44*x^26 + 43*x^25 + 76*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 4*x^18 + 11*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 89*x^9 + 20*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 92*x^2 + 113*x + 92, x^29 + 106*x^27 + 64*x^26 + 83*x^25 + 32*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 86*x^19 + 35*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 49*x^9 + 96*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 10*x^3 + 89*x + 96, x^29 + 106*x^27 + 80*x^26 + 67*x^25 + 64*x^24 + 36*x^23 + 96*x^22 + 89*x^21 + 86*x^19 + 112*x^18 + 115*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 65*x^9 + 64*x^8 + 36*x^7 + 96*x^6 + 75*x^5 + 10*x^3 + 16*x^2 + 9*x + 64, x^29 + 106*x^27 + 116*x^26 + 107*x^25 + 52*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 28*x^18 + 11*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 25*x^9 + 108*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 4*x^2 + 113*x + 100, x^29 + 106*x^27 + 19*x^25 + 32*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 86*x^19 + 64*x^18 + 99*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 113*x^9 + 96*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 10*x^3 + 64*x^2 + 25*x + 96, x^29 + 106*x^27 + 24*x^26 + 19*x^25 + 88*x^24 + 36*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 72*x^18 + 99*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 113*x^9 + 104*x^8 + 36*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 120*x^2 + 25*x + 120, x^29 + 106*x^27 + 32*x^26 + 19*x^25 + 36*x^23 + 57*x^21 + 64*x^20 + 86*x^19 + 32*x^18 + 99*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 113*x^9 + 36*x^7 + 43*x^5 + 64*x^4 + 10*x^3 + 96*x^2 + 25*x + 64, x^29 + 106*x^27 + 72*x^26 + 99*x^25 + 24*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 24*x^18 + 83*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 33*x^9 + 40*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 40*x^2 + 41*x + 120, x^29 + 106*x^27 + 20*x^26 + 59*x^25 + 100*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 124*x^18 + 59*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 73*x^9 + 60*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 36*x^2 + 65*x + 84, x^29 + 106*x^27 + 52*x^26 + 91*x^25 + 68*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 28*x^18 + 91*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 41*x^9 + 92*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 4*x^2 + 33*x + 116, x^29 + 106*x^27 + 108*x^26 + 123*x^25 + 92*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 4*x^18 + 123*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 9*x^9 + 4*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 92*x^2 + x + 108, x^29 + 106*x^27 + 72*x^26 + 67*x^25 + 56*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 88*x^18 + 51*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 65*x^9 + 8*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 104*x^2 + 73*x + 88, x^29 + 106*x^27 + 80*x^26 + 35*x^25 + 64*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 48*x^18 + 83*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 97*x^9 + 64*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 80*x^2 + 41*x, x^29 + 106*x^27 + 40*x^26 + 99*x^25 + 88*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 56*x^18 + 83*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 33*x^9 + 104*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 8*x^2 + 41*x + 56, x^29 + 106*x^27 + 120*x^26 + 3*x^25 + 72*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 104*x^18 + 115*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + x^9 + 120*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 88*x^2 + 9*x + 40, x^29 + 106*x^27 + 76*x^26 + 43*x^25 + 108*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 100*x^18 + 11*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 89*x^9 + 116*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 124*x^2 + 113*x + 124, x^29 + 106*x^27 + 104*x^26 + 3*x^25 + 88*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 56*x^18 + 115*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + x^9 + 104*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 8*x^2 + 9*x + 120, x^29 + 106*x^27 + 100*x^26 + 11*x^25 + 68*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 108*x^18 + 107*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 121*x^9 + 92*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 52*x^2 + 17*x + 52, x^29 + 106*x^27 + 116*x^26 + 27*x^25 + 68*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 92*x^18 + 27*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 105*x^9 + 92*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 68*x^2 + 97*x + 116, x^29 + 106*x^27 + 16*x^26 + 99*x^25 + 32*x^24 + 100*x^23 + 32*x^22 + 89*x^21 + 22*x^19 + 112*x^18 + 19*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 33*x^9 + 96*x^8 + 100*x^7 + 32*x^6 + 75*x^5 + 74*x^3 + 16*x^2 + 105*x + 96, x^29 + 106*x^27 + 64*x^26 + 35*x^25 + 16*x^24 + 36*x^23 + 25*x^21 + 96*x^20 + 86*x^19 + 64*x^18 + 19*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 97*x^9 + 112*x^8 + 36*x^7 + 11*x^5 + 96*x^4 + 10*x^3 + 64*x^2 + 105*x + 80, x^29 + 106*x^27 + 120*x^26 + 67*x^25 + 40*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 104*x^18 + 51*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 65*x^9 + 24*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 88*x^2 + 73*x + 8, x^29 + 106*x^27 + 64*x^26 + 99*x^25 + 112*x^24 + 36*x^23 + 25*x^21 + 32*x^20 + 86*x^19 + 64*x^18 + 83*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 33*x^9 + 16*x^8 + 36*x^7 + 11*x^5 + 32*x^4 + 10*x^3 + 64*x^2 + 41*x + 48, x^29 + 106*x^27 + 104*x^26 + 51*x^25 + 8*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 120*x^18 + 3*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 81*x^9 + 56*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 72*x^2 + 121*x + 40, x^29 + 106*x^27 + 80*x^26 + 19*x^25 + 48*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 48*x^18 + 99*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 113*x^9 + 80*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 80*x^2 + 25*x + 48, x^29 + 106*x^27 + 124*x^26 + 75*x^25 + 28*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 52*x^18 + 43*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 57*x^9 + 68*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 44*x^2 + 81*x + 44, x^29 + 106*x^27 + 44*x^26 + 75*x^25 + 12*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 4*x^18 + 107*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 57*x^9 + 84*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 92*x^2 + 17*x + 28, x^29 + 106*x^27 + 64*x^26 + 99*x^25 + 16*x^24 + 36*x^23 + 25*x^21 + 96*x^20 + 86*x^19 + 64*x^18 + 83*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 33*x^9 + 112*x^8 + 36*x^7 + 11*x^5 + 96*x^4 + 10*x^3 + 64*x^2 + 41*x + 80, x^29 + 106*x^27 + 8*x^26 + 3*x^25 + 88*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 88*x^18 + 51*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + x^9 + 104*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 104*x^2 + 73*x + 56, x^29 + 106*x^27 + 44*x^26 + 59*x^25 + 60*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 68*x^18 + 59*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 73*x^9 + 36*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 28*x^2 + 65*x + 76, x^29 + 106*x^27 + 84*x^26 + 75*x^25 + 116*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 124*x^18 + 107*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 57*x^9 + 44*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 36*x^2 + 17*x + 100, x^29 + 106*x^27 + 60*x^26 + 107*x^25 + 124*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 116*x^18 + 11*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 25*x^9 + 100*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 108*x^2 + 113*x + 12, x^29 + 106*x^27 + 72*x^26 + 99*x^25 + 120*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 88*x^18 + 19*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 33*x^9 + 72*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 104*x^2 + 105*x + 24, x^29 + 106*x^27 + 4*x^26 + 91*x^25 + 116*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 76*x^18 + 27*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 41*x^9 + 44*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 84*x^2 + 97*x + 36, x^29 + 106*x^27 + 72*x^26 + 19*x^25 + 104*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 88*x^18 + 99*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 113*x^9 + 88*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 104*x^2 + 25*x + 72, x^29 + 106*x^27 + 72*x^26 + 35*x^25 + 24*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 88*x^18 + 83*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 97*x^9 + 40*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 104*x^2 + 41*x + 56, x^29 + 106*x^27 + 84*x^26 + 123*x^25 + 4*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 124*x^18 + 59*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 9*x^9 + 28*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 36*x^2 + 65*x + 52, x^29 + 106*x^27 + 99*x^25 + 48*x^24 + 36*x^23 + 25*x^21 + 32*x^20 + 86*x^19 + 83*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 33*x^9 + 80*x^8 + 36*x^7 + 11*x^5 + 32*x^4 + 10*x^3 + 41*x + 112, x^29 + 106*x^27 + 112*x^26 + 67*x^25 + 64*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 16*x^18 + 51*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 65*x^9 + 64*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 112*x^2 + 73*x, x^29 + 106*x^27 + 24*x^26 + 67*x^25 + 8*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 8*x^18 + 115*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 65*x^9 + 56*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 56*x^2 + 9*x + 40, x^29 + 106*x^27 + 48*x^26 + 99*x^25 + 36*x^23 + 32*x^22 + 25*x^21 + 86*x^19 + 16*x^18 + 83*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 33*x^9 + 36*x^7 + 32*x^6 + 11*x^5 + 10*x^3 + 112*x^2 + 41*x, x^29 + 106*x^27 + 84*x^26 + 27*x^25 + 100*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 60*x^18 + 91*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 105*x^9 + 60*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 100*x^2 + 33*x + 84, x^29 + 106*x^27 + 76*x^26 + 107*x^25 + 44*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 100*x^18 + 75*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 25*x^9 + 52*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 124*x^2 + 49*x + 60, x^29 + 106*x^27 + 48*x^26 + 19*x^25 + 16*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 80*x^18 + 99*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 113*x^9 + 112*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 48*x^2 + 25*x + 16, x^29 + 106*x^27 + 40*x^26 + 51*x^25 + 8*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 56*x^18 + 3*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 81*x^9 + 56*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 8*x^2 + 121*x + 40, x^29 + 106*x^27 + 100*x^26 + 43*x^25 + 36*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 108*x^18 + 75*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 89*x^9 + 124*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 52*x^2 + 49*x + 20, x^29 + 106*x^27 + 92*x^26 + 123*x^25 + 76*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 84*x^18 + 123*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 9*x^9 + 20*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 12*x^2 + x + 28, x^29 + 106*x^27 + 72*x^26 + 35*x^25 + 120*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 24*x^18 + 19*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 97*x^9 + 72*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 40*x^2 + 105*x + 88, x^29 + 106*x^27 + 120*x^26 + 115*x^25 + 24*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 104*x^18 + 3*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 17*x^9 + 40*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 88*x^2 + 121*x + 56, x^29 + 106*x^27 + 56*x^26 + 3*x^25 + 8*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 104*x^18 + 51*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + x^9 + 56*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 88*x^2 + 73*x + 40, x^29 + 106*x^27 + 40*x^26 + 115*x^25 + 40*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 120*x^18 + 3*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 17*x^9 + 24*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 72*x^2 + 121*x + 8, x^29 + 106*x^27 + 32*x^26 + 35*x^25 + 48*x^24 + 100*x^23 + 89*x^21 + 96*x^20 + 22*x^19 + 32*x^18 + 83*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 97*x^9 + 80*x^8 + 100*x^7 + 75*x^5 + 96*x^4 + 74*x^3 + 96*x^2 + 41*x + 48, x^29 + 106*x^27 + 120*x^26 + 51*x^25 + 88*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 104*x^18 + 67*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 81*x^9 + 104*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 88*x^2 + 57*x + 120, x^29 + 106*x^27 + 104*x^26 + 99*x^25 + 56*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 120*x^18 + 83*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 33*x^9 + 8*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 72*x^2 + 41*x + 24, x^29 + 106*x^27 + 4*x^26 + 59*x^25 + 116*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 12*x^18 + 123*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 73*x^9 + 44*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 20*x^2 + x + 100, x^29 + 106*x^27 + 120*x^26 + 3*x^25 + 40*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 104*x^18 + 115*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + x^9 + 24*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 88*x^2 + 9*x + 8, x^29 + 106*x^27 + 51*x^25 + 100*x^23 + 57*x^21 + 22*x^19 + 3*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 81*x^9 + 100*x^7 + 43*x^5 + 74*x^3 + 121*x, x^29 + 106*x^27 + 76*x^26 + 91*x^25 + 28*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 100*x^18 + 91*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 41*x^9 + 68*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 124*x^2 + 33*x + 108, x^29 + 106*x^27 + 120*x^26 + 51*x^25 + 120*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 40*x^18 + 3*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 81*x^9 + 72*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 24*x^2 + 121*x + 88, x^29 + 106*x^27 + 104*x^26 + 83*x^25 + 104*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 120*x^18 + 99*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 49*x^9 + 88*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 72*x^2 + 25*x + 8, x^29 + 106*x^27 + 12*x^26 + 11*x^25 + 12*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 36*x^18 + 43*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 121*x^9 + 84*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 60*x^2 + 81*x + 28, x^29 + 106*x^27 + 8*x^26 + 51*x^25 + 8*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 24*x^18 + 67*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 81*x^9 + 56*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 40*x^2 + 57*x + 104, x^29 + 106*x^27 + 88*x^26 + 35*x^25 + 72*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 72*x^18 + 19*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 97*x^9 + 120*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 120*x^2 + 105*x + 104, x^29 + 106*x^27 + 32*x^26 + 51*x^25 + 36*x^23 + 121*x^21 + 64*x^20 + 86*x^19 + 32*x^18 + 67*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 81*x^9 + 36*x^7 + 107*x^5 + 64*x^4 + 10*x^3 + 96*x^2 + 57*x + 64, x^29 + 106*x^27 + 112*x^26 + 3*x^25 + 64*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 86*x^19 + 80*x^18 + 51*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + x^9 + 64*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 10*x^3 + 48*x^2 + 73*x + 64, x^29 + 106*x^27 + 104*x^26 + 67*x^25 + 56*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 120*x^18 + 115*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 65*x^9 + 8*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 72*x^2 + 9*x + 24, x^29 + 106*x^27 + 116*x^26 + 27*x^25 + 68*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 28*x^18 + 91*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 105*x^9 + 92*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 4*x^2 + 33*x + 52, x^29 + 106*x^27 + 88*x^26 + 99*x^25 + 72*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 72*x^18 + 83*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 33*x^9 + 120*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 120*x^2 + 41*x + 104, x^29 + 106*x^27 + 40*x^26 + 3*x^25 + 24*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 56*x^18 + 51*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + x^9 + 40*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 8*x^2 + 73*x + 120, x^29 + 106*x^27 + 60*x^26 + 107*x^25 + 28*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 116*x^18 + 11*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 25*x^9 + 68*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 108*x^2 + 113*x + 44, x^29 + 106*x^27 + 52*x^26 + 59*x^25 + 4*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 28*x^18 + 123*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 73*x^9 + 28*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 4*x^2 + x + 52, x^29 + 106*x^27 + 124*x^26 + 59*x^25 + 12*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 116*x^18 + 123*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 73*x^9 + 84*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 108*x^2 + x + 28, x^29 + 106*x^27 + 40*x^26 + 83*x^25 + 72*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 56*x^18 + 99*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 49*x^9 + 120*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 8*x^2 + 25*x + 104, x^29 + 106*x^27 + 32*x^26 + 115*x^25 + 96*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 22*x^19 + 96*x^18 + 67*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 17*x^9 + 32*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 74*x^3 + 32*x^2 + 57*x + 96, x^29 + 106*x^27 + 72*x^26 + 67*x^25 + 56*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 24*x^18 + 115*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 65*x^9 + 8*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 40*x^2 + 9*x + 24, x^29 + 106*x^27 + 48*x^26 + 35*x^25 + 96*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 16*x^18 + 19*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 97*x^9 + 32*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 112*x^2 + 105*x + 96, x^29 + 106*x^27 + 12*x^26 + 75*x^25 + 12*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 36*x^18 + 107*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 57*x^9 + 84*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 60*x^2 + 17*x + 28, x^29 + 106*x^27 + 124*x^26 + 107*x^25 + 60*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 116*x^18 + 75*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 25*x^9 + 36*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 108*x^2 + 49*x + 12, x^29 + 106*x^27 + 92*x^26 + 123*x^25 + 108*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 84*x^18 + 123*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 9*x^9 + 116*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 12*x^2 + x + 60, x^29 + 106*x^27 + 124*x^26 + 91*x^25 + 108*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 116*x^18 + 91*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 41*x^9 + 116*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 108*x^2 + 33*x + 124, x^29 + 106*x^27 + 116*x^26 + 123*x^25 + 68*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 92*x^18 + 59*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 9*x^9 + 92*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 68*x^2 + 65*x + 116, x^29 + 106*x^27 + 20*x^26 + 11*x^25 + 20*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 124*x^18 + 107*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 121*x^9 + 12*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 36*x^2 + 17*x + 68, x^29 + 106*x^27 + 28*x^26 + 91*x^25 + 12*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 20*x^18 + 27*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 41*x^9 + 84*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 76*x^2 + 97*x + 92, x^29 + 106*x^27 + 116*x^26 + 107*x^25 + 116*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 92*x^18 + 75*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 25*x^9 + 44*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 68*x^2 + 49*x + 100, x^29 + 106*x^27 + 56*x^26 + 67*x^25 + 72*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 40*x^18 + 51*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 65*x^9 + 120*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 24*x^2 + 73*x + 40, x^29 + 106*x^27 + 92*x^26 + 43*x^25 + 124*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 20*x^18 + 11*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 89*x^9 + 100*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 76*x^2 + 113*x + 76, x^29 + 106*x^27 + 12*x^26 + 11*x^25 + 108*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 36*x^18 + 43*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 121*x^9 + 116*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 60*x^2 + 81*x + 124, x^29 + 106*x^27 + 24*x^26 + 3*x^25 + 104*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 8*x^18 + 51*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + x^9 + 88*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 56*x^2 + 73*x + 8, x^29 + 106*x^27 + 108*x^26 + 123*x^25 + 92*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 68*x^18 + 59*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 9*x^9 + 4*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 28*x^2 + 65*x + 44, x^29 + 106*x^27 + 64*x^26 + 51*x^25 + 96*x^24 + 100*x^23 + 57*x^21 + 64*x^20 + 22*x^19 + 64*x^18 + 3*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 81*x^9 + 32*x^8 + 100*x^7 + 43*x^5 + 64*x^4 + 74*x^3 + 64*x^2 + 121*x + 96, x^29 + 106*x^27 + 56*x^26 + 35*x^25 + 104*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 40*x^18 + 83*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 97*x^9 + 88*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 24*x^2 + 41*x + 72, x^29 + 106*x^27 + 68*x^26 + 11*x^25 + 36*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 76*x^18 + 43*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 121*x^9 + 124*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 84*x^2 + 81*x + 84, x^29 + 106*x^27 + 16*x^26 + 99*x^25 + 32*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 48*x^18 + 83*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 33*x^9 + 96*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 80*x^2 + 41*x + 32, x^29 + 106*x^27 + 4*x^26 + 27*x^25 + 52*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 12*x^18 + 27*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 105*x^9 + 108*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 20*x^2 + 97*x + 36, x^29 + 106*x^27 + 124*x^26 + 75*x^25 + 60*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 52*x^18 + 43*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 57*x^9 + 36*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 44*x^2 + 81*x + 76, x^29 + 106*x^27 + 76*x^26 + 107*x^25 + 76*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 100*x^18 + 75*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 25*x^9 + 20*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 124*x^2 + 49*x + 92, x^29 + 106*x^27 + 48*x^26 + 115*x^25 + 48*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 16*x^18 + 67*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 17*x^9 + 80*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 112*x^2 + 57*x + 112, x^29 + 106*x^27 + 24*x^26 + 51*x^25 + 56*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 8*x^18 + 3*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 40*x^10 + 81*x^9 + 8*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 56*x^2 + 121*x + 24, x^29 + 106*x^27 + 80*x^26 + 99*x^25 + 96*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 112*x^18 + 83*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 33*x^9 + 32*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 16*x^2 + 41*x + 96, x^29 + 106*x^27 + 4*x^26 + 91*x^25 + 84*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 12*x^18 + 91*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 41*x^9 + 76*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 20*x^2 + 33*x + 68, x^29 + 106*x^27 + 8*x^26 + 3*x^25 + 88*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 24*x^18 + 115*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + x^9 + 104*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 40*x^2 + 9*x + 120, x^29 + 106*x^27 + 84*x^26 + 107*x^25 + 52*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 124*x^18 + 75*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 25*x^9 + 108*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 36*x^2 + 49*x + 36, x^29 + 106*x^27 + 100*x^26 + 123*x^25 + 116*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 108*x^18 + 123*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 9*x^9 + 44*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 52*x^2 + x + 36, x^29 + 106*x^27 + 92*x^26 + 43*x^25 + 92*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 20*x^18 + 11*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 89*x^9 + 4*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 76*x^2 + 113*x + 44, x^29 + 106*x^27 + 44*x^26 + 59*x^25 + 28*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 68*x^18 + 59*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 73*x^9 + 68*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 28*x^2 + 65*x + 44, x^29 + 106*x^27 + 4*x^26 + 107*x^25 + 100*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 12*x^18 + 75*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 25*x^9 + 60*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 20*x^2 + 49*x + 20, x^29 + 106*x^27 + 112*x^26 + 83*x^25 + 80*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 80*x^18 + 99*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 49*x^9 + 48*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 48*x^2 + 25*x + 16, x^29 + 106*x^27 + 52*x^26 + 123*x^25 + 68*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 92*x^18 + 123*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 9*x^9 + 92*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 68*x^2 + x + 52, x^29 + 106*x^27 + 112*x^26 + 83*x^25 + 112*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 16*x^18 + 35*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 49*x^9 + 16*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 112*x^2 + 89*x + 112, x^29 + 106*x^27 + 40*x^26 + 115*x^25 + 72*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 56*x^18 + 67*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 17*x^9 + 120*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 8*x^2 + 57*x + 104, x^29 + 106*x^27 + 52*x^26 + 107*x^25 + 116*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 28*x^18 + 75*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 25*x^9 + 44*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 4*x^2 + 49*x + 100, x^29 + 106*x^27 + 80*x^26 + 115*x^25 + 112*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 112*x^18 + 67*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 17*x^9 + 16*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 16*x^2 + 57*x + 48, x^29 + 106*x^27 + 68*x^26 + 11*x^25 + 4*x^24 + 68*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 76*x^18 + 43*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 121*x^9 + 28*x^8 + 68*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 84*x^2 + 81*x + 52, x^29 + 106*x^27 + 92*x^26 + 91*x^25 + 44*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 20*x^18 + 91*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 41*x^9 + 52*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 76*x^2 + 33*x + 60, x^29 + 106*x^27 + 44*x^26 + 123*x^25 + 92*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 68*x^18 + 123*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 9*x^9 + 4*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 28*x^2 + x + 108, x^29 + 106*x^27 + 100*x^26 + 59*x^25 + 20*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 108*x^18 + 59*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 73*x^9 + 12*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 52*x^2 + 65*x + 68, x^29 + 106*x^27 + 32*x^26 + 51*x^25 + 32*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 22*x^19 + 96*x^18 + 3*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 81*x^9 + 96*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 74*x^3 + 32*x^2 + 121*x + 32, x^29 + 106*x^27 + 84*x^26 + 27*x^25 + 68*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 60*x^18 + 91*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 105*x^9 + 92*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 100*x^2 + 33*x + 52, x^29 + 106*x^27 + 12*x^26 + 27*x^25 + 92*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 100*x^18 + 91*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 105*x^9 + 4*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 124*x^2 + 33*x + 108, x^29 + 106*x^27 + 8*x^26 + 115*x^25 + 104*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 24*x^18 + 3*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 17*x^9 + 88*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 40*x^2 + 121*x + 72, x^29 + 106*x^27 + 64*x^26 + 19*x^25 + 36*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 86*x^19 + 99*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 113*x^9 + 36*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 10*x^3 + 25*x + 64, x^29 + 106*x^27 + 124*x^26 + 11*x^25 + 124*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 52*x^18 + 107*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 121*x^9 + 100*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 44*x^2 + 17*x + 12, x^29 + 106*x^27 + 76*x^26 + 11*x^25 + 108*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 100*x^18 + 43*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 121*x^9 + 116*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 124*x^2 + 81*x + 124, x^29 + 106*x^27 + 16*x^26 + 83*x^25 + 80*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 48*x^18 + 99*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 49*x^9 + 48*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 80*x^2 + 25*x + 16, x^29 + 106*x^27 + 124*x^26 + 11*x^25 + 60*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 52*x^18 + 107*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 121*x^9 + 36*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 44*x^2 + 17*x + 76, x^29 + 106*x^27 + 88*x^26 + 99*x^25 + 104*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 72*x^18 + 83*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 33*x^9 + 88*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 120*x^2 + 41*x + 8, x^29 + 106*x^27 + 40*x^26 + 3*x^25 + 120*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 120*x^18 + 115*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + x^9 + 72*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 72*x^2 + 9*x + 24, x^29 + 106*x^27 + 40*x^26 + 19*x^25 + 8*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 56*x^18 + 35*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 113*x^9 + 56*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 8*x^2 + 89*x + 40, x^29 + 106*x^27 + 80*x^26 + 35*x^25 + 36*x^23 + 96*x^22 + 25*x^21 + 86*x^19 + 112*x^18 + 19*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 97*x^9 + 36*x^7 + 96*x^6 + 11*x^5 + 10*x^3 + 16*x^2 + 105*x, x^29 + 106*x^27 + 20*x^26 + 91*x^25 + 4*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 60*x^18 + 91*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 41*x^9 + 28*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 100*x^2 + 33*x + 52, x^29 + 106*x^27 + 12*x^26 + 11*x^25 + 76*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 36*x^18 + 43*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 121*x^9 + 20*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 60*x^2 + 81*x + 92, x^29 + 106*x^27 + 44*x^26 + 91*x^25 + 92*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 4*x^18 + 91*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 41*x^9 + 4*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 92*x^2 + 33*x + 44, x^29 + 106*x^27 + 12*x^26 + 75*x^25 + 108*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 36*x^18 + 107*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 57*x^9 + 116*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 60*x^2 + 17*x + 124, x^29 + 106*x^27 + 36*x^26 + 59*x^25 + 52*x^24 + 4*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 108*x^18 + 123*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 73*x^9 + 108*x^8 + 4*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 52*x^2 + x + 36, x^29 + 106*x^27 + 16*x^26 + 3*x^25 + 100*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 112*x^18 + 115*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + x^9 + 100*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 16*x^2 + 9*x + 64, x^29 + 106*x^27 + 104*x^26 + 19*x^25 + 8*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 56*x^18 + 99*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 113*x^9 + 56*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 8*x^2 + 25*x + 104, x^29 + 106*x^27 + 56*x^26 + 115*x^25 + 120*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 104*x^18 + 67*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 17*x^9 + 72*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 88*x^2 + 57*x + 88, x^29 + 106*x^27 + 92*x^26 + 123*x^25 + 12*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 20*x^18 + 59*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 9*x^9 + 84*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 76*x^2 + 65*x + 28, x^29 + 106*x^27 + 76*x^26 + 59*x^25 + 28*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 54*x^19 + 100*x^18 + 123*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 73*x^9 + 68*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 106*x^3 + 124*x^2 + x + 108, x^29 + 106*x^27 + 52*x^26 + 123*x^25 + 68*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 28*x^18 + 59*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 9*x^9 + 92*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 4*x^2 + 65*x + 116, x^29 + 106*x^27 + 60*x^26 + 91*x^25 + 44*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 52*x^18 + 91*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 41*x^9 + 52*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 44*x^2 + 33*x + 60, x^29 + 106*x^27 + 64*x^26 + 3*x^25 + 48*x^24 + 100*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 22*x^19 + 115*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + x^9 + 80*x^8 + 100*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 74*x^3 + 9*x + 48, x^29 + 106*x^27 + 64*x^26 + 19*x^25 + 100*x^23 + 121*x^21 + 22*x^19 + 64*x^18 + 35*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 113*x^9 + 100*x^7 + 107*x^5 + 74*x^3 + 64*x^2 + 89*x, x^29 + 106*x^27 + 44*x^26 + 75*x^25 + 44*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 4*x^18 + 107*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 57*x^9 + 52*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 92*x^2 + 17*x + 60, x^29 + 106*x^27 + 20*x^26 + 27*x^25 + 100*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 124*x^18 + 91*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 105*x^9 + 60*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 36*x^2 + 33*x + 84, x^29 + 106*x^27 + 8*x^26 + 115*x^25 + 72*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 24*x^18 + 3*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 17*x^9 + 120*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 40*x^2 + 121*x + 40, x^29 + 106*x^27 + 108*x^26 + 27*x^25 + 92*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 4*x^18 + 91*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 105*x^9 + 4*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 92*x^2 + 33*x + 108, x^29 + 106*x^27 + 19*x^25 + 36*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 86*x^19 + 64*x^18 + 99*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 113*x^9 + 36*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 10*x^3 + 64*x^2 + 25*x + 64, x^29 + 106*x^27 + 120*x^26 + 19*x^25 + 120*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 40*x^18 + 35*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 113*x^9 + 72*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 24*x^2 + 89*x + 88, x^29 + 106*x^27 + 28*x^26 + 27*x^25 + 12*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 20*x^18 + 91*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 105*x^9 + 84*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 76*x^2 + 33*x + 92, x^29 + 106*x^27 + 56*x^26 + 19*x^25 + 56*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 22*x^19 + 104*x^18 + 35*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 113*x^9 + 8*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 74*x^3 + 88*x^2 + 89*x + 24, x^29 + 106*x^27 + 80*x^26 + 115*x^25 + 80*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 48*x^18 + 3*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 17*x^9 + 48*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 80*x^2 + 121*x + 80, x^29 + 106*x^27 + 44*x^26 + 43*x^25 + 44*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 68*x^18 + 75*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 89*x^9 + 52*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 28*x^2 + 49*x + 124, x^29 + 106*x^27 + 36*x^26 + 27*x^25 + 20*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 108*x^18 + 27*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 105*x^9 + 12*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 52*x^2 + 97*x + 4, x^29 + 106*x^27 + 116*x^26 + 11*x^25 + 52*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 92*x^18 + 43*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 121*x^9 + 108*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 68*x^2 + 81*x + 36, x^29 + 106*x^27 + 24*x^26 + 3*x^25 + 8*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 8*x^18 + 51*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + x^9 + 56*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 56*x^2 + 73*x + 40, x^29 + 106*x^27 + 108*x^26 + 91*x^25 + 60*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 4*x^18 + 27*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 41*x^9 + 36*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 92*x^2 + 97*x + 76, x^29 + 106*x^27 + 4*x^26 + 43*x^25 + 4*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 76*x^18 + 75*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 89*x^9 + 28*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 84*x^2 + 49*x + 116, x^29 + 106*x^27 + 4*x^26 + 91*x^25 + 20*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 12*x^18 + 91*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 41*x^9 + 12*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 20*x^2 + 33*x + 4, x^29 + 106*x^27 + 4*x^26 + 27*x^25 + 20*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 76*x^18 + 91*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 105*x^9 + 12*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 84*x^2 + 33*x + 68, x^29 + 106*x^27 + 36*x^26 + 123*x^25 + 84*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 44*x^18 + 123*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 9*x^9 + 76*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 116*x^2 + x + 4, x^29 + 106*x^27 + 4*x^26 + 43*x^25 + 100*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 76*x^18 + 75*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 89*x^9 + 60*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 84*x^2 + 49*x + 84, x^29 + 106*x^27 + 8*x^26 + 115*x^25 + 72*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 88*x^18 + 67*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 17*x^9 + 120*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 104*x^2 + 57*x + 104, x^29 + 106*x^27 + 104*x^26 + 35*x^25 + 88*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 120*x^18 + 19*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 97*x^9 + 104*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 72*x^2 + 105*x + 56, x^29 + 106*x^27 + 116*x^26 + 43*x^25 + 84*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 92*x^18 + 11*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 89*x^9 + 76*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 68*x^2 + 113*x + 68, x^29 + 106*x^27 + 116*x^26 + 59*x^25 + 4*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 28*x^18 + 59*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 73*x^9 + 28*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 4*x^2 + 65*x + 116, x^29 + 106*x^27 + 76*x^26 + 75*x^25 + 76*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 36*x^18 + 43*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 57*x^9 + 20*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 60*x^2 + 81*x + 28, x^29 + 106*x^27 + 12*x^26 + 123*x^25 + 124*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 36*x^18 + 59*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 9*x^9 + 100*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 60*x^2 + 65*x + 76, x^29 + 106*x^27 + 32*x^26 + 67*x^25 + 16*x^24 + 100*x^23 + 25*x^21 + 32*x^20 + 22*x^19 + 32*x^18 + 51*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 65*x^9 + 112*x^8 + 100*x^7 + 11*x^5 + 32*x^4 + 74*x^3 + 96*x^2 + 73*x + 16, x^29 + 106*x^27 + 88*x^26 + 51*x^25 + 24*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 8*x^18 + 67*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 81*x^9 + 40*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 56*x^2 + 57*x + 56, x^29 + 106*x^27 + 36*x^26 + 91*x^25 + 116*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 108*x^18 + 91*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 41*x^9 + 44*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 52*x^2 + 33*x + 100, x^29 + 106*x^27 + 52*x^26 + 11*x^25 + 52*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 28*x^18 + 43*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 121*x^9 + 108*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 4*x^2 + 81*x + 36, x^29 + 106*x^27 + 120*x^26 + 115*x^25 + 120*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 104*x^18 + 3*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 17*x^9 + 72*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 88*x^2 + 121*x + 24, x^29 + 106*x^27 + 44*x^26 + 59*x^25 + 60*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 4*x^18 + 123*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 73*x^9 + 36*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 92*x^2 + x + 12, x^29 + 106*x^27 + 52*x^26 + 75*x^25 + 116*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 28*x^18 + 107*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 57*x^9 + 44*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 4*x^2 + 17*x + 100, x^29 + 106*x^27 + 104*x^26 + 67*x^25 + 120*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 120*x^18 + 115*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 65*x^9 + 72*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 72*x^2 + 9*x + 88, x^29 + 106*x^27 + 56*x^26 + 67*x^25 + 104*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 40*x^18 + 51*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 65*x^9 + 88*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 24*x^2 + 73*x + 72, x^29 + 106*x^27 + 92*x^26 + 75*x^25 + 92*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 84*x^18 + 43*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 57*x^9 + 4*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 12*x^2 + 81*x + 108, x^29 + 106*x^27 + 100*x^26 + 123*x^25 + 52*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 108*x^18 + 123*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 9*x^9 + 108*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 52*x^2 + x + 100, x^29 + 106*x^27 + 60*x^26 + 91*x^25 + 12*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 52*x^18 + 91*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 41*x^9 + 84*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 44*x^2 + 33*x + 28, x^29 + 106*x^27 + 64*x^26 + 115*x^25 + 100*x^23 + 57*x^21 + 22*x^19 + 64*x^18 + 67*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 17*x^9 + 100*x^7 + 43*x^5 + 74*x^3 + 64*x^2 + 57*x, x^29 + 106*x^27 + 44*x^26 + 43*x^25 + 108*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 68*x^18 + 75*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 89*x^9 + 116*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 28*x^2 + 49*x + 60, x^29 + 106*x^27 + 100*x^26 + 11*x^25 + 4*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 118*x^19 + 44*x^18 + 43*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 121*x^9 + 28*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 42*x^3 + 116*x^2 + 81*x + 52, x^29 + 106*x^27 + 72*x^26 + 3*x^25 + 56*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 24*x^18 + 51*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + x^9 + 8*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 40*x^2 + 73*x + 24, x^29 + 106*x^27 + 36*x^26 + 107*x^25 + 4*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 44*x^18 + 11*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 25*x^9 + 28*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 116*x^2 + 113*x + 116, x^29 + 106*x^27 + 92*x^26 + 59*x^25 + 108*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 84*x^18 + 59*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 73*x^9 + 116*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 12*x^2 + 65*x + 60, x^29 + 106*x^27 + 64*x^26 + 3*x^25 + 112*x^24 + 36*x^23 + 89*x^21 + 32*x^20 + 86*x^19 + 64*x^18 + 51*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + x^9 + 16*x^8 + 36*x^7 + 75*x^5 + 32*x^4 + 10*x^3 + 64*x^2 + 73*x + 48, x^29 + 106*x^27 + 124*x^26 + 27*x^25 + 44*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 116*x^18 + 27*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 105*x^9 + 52*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 108*x^2 + 97*x + 60, x^29 + 106*x^27 + 36*x^26 + 91*x^25 + 116*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 44*x^18 + 27*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 41*x^9 + 44*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 116*x^2 + 97*x + 36, x^29 + 106*x^27 + 20*x^26 + 11*x^25 + 20*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 60*x^18 + 43*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 121*x^9 + 12*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 100*x^2 + 81*x + 4, x^29 + 106*x^27 + 84*x^26 + 43*x^25 + 52*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 124*x^18 + 11*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 89*x^9 + 108*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 36*x^2 + 113*x + 36, x^29 + 106*x^27 + 20*x^26 + 107*x^25 + 84*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 124*x^18 + 11*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 25*x^9 + 76*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 36*x^2 + 113*x + 4, x^29 + 106*x^27 + 100*x^26 + 91*x^25 + 84*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 108*x^18 + 27*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 41*x^9 + 76*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 52*x^2 + 97*x + 4, x^29 + 106*x^27 + 72*x^26 + 51*x^25 + 72*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 88*x^18 + 67*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 81*x^9 + 120*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 104*x^2 + 57*x + 40, x^29 + 106*x^27 + 80*x^26 + 19*x^25 + 112*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 22*x^19 + 112*x^18 + 35*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 113*x^9 + 16*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 74*x^3 + 16*x^2 + 89*x + 48, x^29 + 106*x^27 + 20*x^26 + 11*x^25 + 52*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 60*x^18 + 43*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 121*x^9 + 108*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 100*x^2 + 81*x + 36, x^29 + 106*x^27 + 88*x^26 + 99*x^25 + 40*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 8*x^18 + 19*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 33*x^9 + 24*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 56*x^2 + 105*x + 8, x^29 + 106*x^27 + 84*x^26 + 59*x^25 + 36*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 124*x^18 + 123*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 73*x^9 + 124*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 36*x^2 + x + 84, x^29 + 106*x^27 + 44*x^26 + 91*x^25 + 92*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 68*x^18 + 27*x^17 + 52*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 41*x^9 + 4*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 28*x^2 + 97*x + 108, x^29 + 106*x^27 + 92*x^26 + 11*x^25 + 124*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 20*x^18 + 43*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 121*x^9 + 100*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 76*x^2 + 81*x + 76, x^29 + 106*x^27 + 8*x^26 + 99*x^25 + 56*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 16*x^20 + 22*x^19 + 24*x^18 + 19*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 33*x^9 + 8*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 16*x^4 + 74*x^3 + 40*x^2 + 105*x + 88, x^29 + 106*x^27 + 108*x^26 + 27*x^25 + 124*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 68*x^18 + 27*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 105*x^9 + 100*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 28*x^2 + 97*x + 76, x^29 + 106*x^27 + 8*x^26 + 51*x^25 + 72*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 24*x^18 + 67*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 81*x^9 + 120*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 40*x^2 + 57*x + 40, x^29 + 106*x^27 + 100*x^26 + 75*x^25 + 36*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 108*x^18 + 43*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 57*x^9 + 124*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 52*x^2 + 81*x + 20, x^29 + 106*x^27 + 28*x^26 + 75*x^25 + 92*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 84*x^18 + 107*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 57*x^9 + 4*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 12*x^2 + 17*x + 44, x^29 + 106*x^27 + 44*x^26 + 107*x^25 + 76*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 4*x^18 + 75*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 25*x^9 + 20*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 92*x^2 + 49*x + 92, x^29 + 106*x^27 + 12*x^26 + 43*x^25 + 44*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 100*x^18 + 75*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 89*x^9 + 52*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 124*x^2 + 49*x + 124, x^29 + 106*x^27 + 48*x^26 + 99*x^25 + 100*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 80*x^18 + 19*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 33*x^9 + 100*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 48*x^2 + 105*x + 64, x^29 + 106*x^27 + 64*x^26 + 83*x^25 + 96*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 86*x^19 + 35*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 49*x^9 + 32*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 10*x^3 + 89*x + 32, x^29 + 106*x^27 + 124*x^26 + 11*x^25 + 28*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 52*x^18 + 107*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 121*x^9 + 68*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 44*x^2 + 17*x + 44, x^29 + 106*x^27 + 116*x^26 + 75*x^25 + 84*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 28*x^18 + 43*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 57*x^9 + 76*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 4*x^2 + 81*x + 4, x^29 + 106*x^27 + 96*x^26 + 35*x^25 + 16*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 86*x^19 + 32*x^18 + 19*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 97*x^9 + 112*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 10*x^3 + 96*x^2 + 105*x + 80, x^29 + 106*x^27 + 60*x^26 + 43*x^25 + 124*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 52*x^18 + 11*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 89*x^9 + 100*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 44*x^2 + 113*x + 76, x^29 + 106*x^27 + 92*x^26 + 11*x^25 + 92*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 20*x^18 + 43*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 121*x^9 + 4*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 76*x^2 + 81*x + 44, x^29 + 106*x^27 + 52*x^26 + 75*x^25 + 52*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 28*x^18 + 107*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 57*x^9 + 108*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 4*x^2 + 17*x + 36, x^29 + 106*x^27 + 96*x^26 + 51*x^25 + 64*x^24 + 100*x^23 + 64*x^22 + 57*x^21 + 22*x^19 + 32*x^18 + 3*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 81*x^9 + 64*x^8 + 100*x^7 + 64*x^6 + 43*x^5 + 74*x^3 + 96*x^2 + 121*x + 64, x^29 + 106*x^27 + 48*x^26 + 83*x^25 + 80*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 16*x^18 + 99*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 49*x^9 + 48*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 112*x^2 + 25*x + 16, x^29 + 106*x^27 + 120*x^26 + 99*x^25 + 72*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 104*x^18 + 19*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 33*x^9 + 120*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 88*x^2 + 105*x + 40, x^29 + 106*x^27 + 80*x^26 + 83*x^25 + 80*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 48*x^18 + 35*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 49*x^9 + 48*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 80*x^2 + 89*x + 80, x^29 + 106*x^27 + 96*x^26 + 115*x^25 + 36*x^23 + 121*x^21 + 64*x^20 + 86*x^19 + 96*x^18 + 3*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 17*x^9 + 36*x^7 + 107*x^5 + 64*x^4 + 10*x^3 + 32*x^2 + 121*x + 64, x^29 + 106*x^27 + 68*x^26 + 123*x^25 + 116*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 54*x^19 + 76*x^18 + 59*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 9*x^9 + 44*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 106*x^3 + 84*x^2 + 65*x + 100, x^29 + 106*x^27 + 84*x^26 + 123*x^25 + 4*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 60*x^18 + 123*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 9*x^9 + 28*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 100*x^2 + x + 116, x^29 + 106*x^27 + 35*x^25 + 48*x^24 + 36*x^23 + 25*x^21 + 32*x^20 + 86*x^19 + 19*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 97*x^9 + 80*x^8 + 36*x^7 + 11*x^5 + 32*x^4 + 10*x^3 + 105*x + 112, x^29 + 106*x^27 + 84*x^26 + 123*x^25 + 100*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 124*x^18 + 59*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 9*x^9 + 60*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 36*x^2 + 65*x + 20, x^29 + 106*x^27 + 76*x^26 + 43*x^25 + 44*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 100*x^18 + 11*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 89*x^9 + 52*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 124*x^2 + 113*x + 60, x^29 + 106*x^27 + 44*x^26 + 123*x^25 + 28*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 68*x^18 + 123*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 9*x^9 + 68*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 28*x^2 + x + 44, x^29 + 106*x^27 + 120*x^26 + 35*x^25 + 104*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 40*x^18 + 19*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 97*x^9 + 88*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 24*x^2 + 105*x + 8, x^29 + 106*x^27 + 40*x^26 + 35*x^25 + 24*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 56*x^18 + 19*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 97*x^9 + 40*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 8*x^2 + 105*x + 120, x^29 + 106*x^27 + 112*x^26 + 115*x^25 + 80*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 16*x^18 + 3*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 17*x^9 + 48*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 112*x^2 + 121*x + 80, x^29 + 106*x^27 + 24*x^26 + 3*x^25 + 72*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 8*x^18 + 51*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + x^9 + 120*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 56*x^2 + 73*x + 104, x^29 + 106*x^27 + 108*x^26 + 43*x^25 + 44*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 4*x^18 + 75*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 89*x^9 + 52*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 92*x^2 + 49*x + 124, x^29 + 106*x^27 + 116*x^26 + 91*x^25 + 36*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 92*x^18 + 91*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 41*x^9 + 124*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 68*x^2 + 33*x + 84, x^29 + 106*x^27 + 124*x^26 + 43*x^25 + 124*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 52*x^18 + 75*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 89*x^9 + 100*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 44*x^2 + 49*x + 12, x^29 + 106*x^27 + 120*x^26 + 35*x^25 + 8*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 104*x^18 + 83*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 97*x^9 + 56*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 88*x^2 + 41*x + 104, x^29 + 106*x^27 + 100*x^26 + 43*x^25 + 36*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 44*x^18 + 11*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 89*x^9 + 124*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 116*x^2 + 113*x + 84, x^29 + 106*x^27 + 48*x^26 + 115*x^25 + 80*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 16*x^18 + 67*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 17*x^9 + 48*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 112*x^2 + 57*x + 16, x^29 + 106*x^27 + 12*x^26 + 43*x^25 + 108*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 100*x^18 + 75*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 89*x^9 + 116*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 124*x^2 + 49*x + 60, x^29 + 106*x^27 + 40*x^26 + 19*x^25 + 104*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 56*x^18 + 35*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 113*x^9 + 88*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 8*x^2 + 89*x + 8, x^29 + 106*x^27 + 36*x^26 + 91*x^25 + 84*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 44*x^18 + 27*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 41*x^9 + 76*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 116*x^2 + 97*x + 4, x^29 + 106*x^27 + 92*x^26 + 11*x^25 + 28*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 20*x^18 + 43*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 121*x^9 + 68*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 76*x^2 + 81*x + 108, x^29 + 106*x^27 + 32*x^26 + 83*x^25 + 96*x^24 + 36*x^23 + 57*x^21 + 86*x^19 + 32*x^18 + 35*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 49*x^9 + 32*x^8 + 36*x^7 + 43*x^5 + 10*x^3 + 96*x^2 + 89*x + 32, x^29 + 106*x^27 + 76*x^26 + 75*x^25 + 12*x^24 + 4*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 36*x^18 + 43*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 57*x^9 + 84*x^8 + 4*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 60*x^2 + 81*x + 92, x^29 + 106*x^27 + 64*x^26 + 19*x^25 + 96*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 86*x^19 + 99*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 113*x^9 + 32*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 10*x^3 + 25*x + 32, x^29 + 106*x^27 + 104*x^26 + 35*x^25 + 88*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 56*x^18 + 83*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 97*x^9 + 104*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 8*x^2 + 41*x + 120, x^29 + 106*x^27 + 72*x^26 + 83*x^25 + 40*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 24*x^18 + 99*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 49*x^9 + 24*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 40*x^2 + 25*x + 72, x^29 + 106*x^27 + 12*x^26 + 107*x^25 + 76*x^24 + 4*x^23 + 8*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 100*x^18 + 11*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 25*x^9 + 20*x^8 + 4*x^7 + 72*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 124*x^2 + 113*x + 28, x^29 + 106*x^27 + 4*x^26 + 91*x^25 + 52*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 12*x^18 + 91*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 41*x^9 + 108*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 20*x^2 + 33*x + 36, x^29 + 106*x^27 + 83*x^25 + 96*x^24 + 36*x^23 + 64*x^22 + 57*x^21 + 86*x^19 + 64*x^18 + 35*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 49*x^9 + 32*x^8 + 36*x^7 + 64*x^6 + 43*x^5 + 10*x^3 + 64*x^2 + 89*x + 32, x^29 + 106*x^27 + 72*x^26 + 67*x^25 + 24*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 88*x^18 + 51*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 65*x^9 + 40*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 104*x^2 + 73*x + 56, x^29 + 106*x^27 + 56*x^26 + 115*x^25 + 56*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 40*x^18 + 3*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 17*x^9 + 8*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 24*x^2 + 121*x + 88, x^29 + 106*x^27 + 96*x^26 + 35*x^25 + 80*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 86*x^19 + 32*x^18 + 19*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 97*x^9 + 48*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 10*x^3 + 96*x^2 + 105*x + 16, x^29 + 106*x^27 + 100*x^26 + 91*x^25 + 116*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 108*x^18 + 27*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 41*x^9 + 44*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 52*x^2 + 97*x + 36, x^29 + 106*x^27 + 32*x^26 + 83*x^25 + 32*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 22*x^19 + 96*x^18 + 99*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 49*x^9 + 96*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 74*x^3 + 32*x^2 + 25*x + 32, x^29 + 106*x^27 + 3*x^25 + 112*x^24 + 36*x^23 + 89*x^21 + 32*x^20 + 86*x^19 + 51*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + x^9 + 16*x^8 + 36*x^7 + 75*x^5 + 32*x^4 + 10*x^3 + 73*x + 48, x^29 + 106*x^27 + 56*x^26 + 83*x^25 + 120*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 40*x^18 + 35*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 49*x^9 + 72*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 24*x^2 + 89*x + 24, x^29 + 106*x^27 + 52*x^26 + 27*x^25 + 68*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 92*x^18 + 91*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 105*x^9 + 92*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 68*x^2 + 33*x + 52, x^29 + 106*x^27 + 84*x^26 + 123*x^25 + 36*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 60*x^18 + 123*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 9*x^9 + 124*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 100*x^2 + x + 20, x^29 + 106*x^27 + 84*x^26 + 59*x^25 + 4*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 60*x^18 + 59*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 73*x^9 + 28*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 100*x^2 + 65*x + 116, x^29 + 106*x^27 + 100*x^26 + 75*x^25 + 4*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 108*x^18 + 43*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 57*x^9 + 28*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 52*x^2 + 81*x + 116, x^29 + 106*x^27 + 80*x^26 + 51*x^25 + 48*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 48*x^18 + 67*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 81*x^9 + 80*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 80*x^2 + 57*x + 48, x^29 + 106*x^27 + 35*x^25 + 112*x^24 + 36*x^23 + 25*x^21 + 32*x^20 + 86*x^19 + 19*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 97*x^9 + 16*x^8 + 36*x^7 + 11*x^5 + 32*x^4 + 10*x^3 + 105*x + 48, x^29 + 106*x^27 + 116*x^26 + 75*x^25 + 20*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 92*x^18 + 107*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 57*x^9 + 12*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 68*x^2 + 17*x + 4, x^29 + 106*x^27 + 80*x^26 + 19*x^25 + 16*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 48*x^18 + 99*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 113*x^9 + 112*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 80*x^2 + 25*x + 16, x^29 + 106*x^27 + 88*x^26 + 115*x^25 + 88*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 72*x^18 + 67*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 17*x^9 + 104*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 120*x^2 + 57*x + 56, x^29 + 106*x^27 + 60*x^26 + 75*x^25 + 28*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 52*x^18 + 107*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 57*x^9 + 68*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 44*x^2 + 17*x + 108, x^29 + 106*x^27 + 116*x^26 + 75*x^25 + 52*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 92*x^18 + 107*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 57*x^9 + 108*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 68*x^2 + 17*x + 36, x^29 + 106*x^27 + 88*x^26 + 35*x^25 + 104*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 8*x^18 + 83*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 97*x^9 + 88*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 56*x^2 + 41*x + 72, x^29 + 106*x^27 + 88*x^26 + 67*x^25 + 104*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 72*x^18 + 115*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 65*x^9 + 88*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 120*x^2 + 9*x + 8, x^29 + 106*x^27 + 92*x^26 + 43*x^25 + 60*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 20*x^18 + 11*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 89*x^9 + 36*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 76*x^2 + 113*x + 12, x^29 + 106*x^27 + 108*x^26 + 107*x^25 + 76*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 4*x^18 + 11*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 25*x^9 + 20*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 92*x^2 + 113*x + 28, x^29 + 106*x^27 + 124*x^26 + 59*x^25 + 44*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 52*x^18 + 59*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 73*x^9 + 52*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 44*x^2 + 65*x + 124, x^29 + 106*x^27 + 116*x^26 + 43*x^25 + 116*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 92*x^18 + 11*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 89*x^9 + 44*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 68*x^2 + 113*x + 100, x^29 + 106*x^27 + 116*x^26 + 123*x^25 + 100*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 92*x^18 + 59*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 9*x^9 + 60*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 68*x^2 + 65*x + 20, x^29 + 106*x^27 + 104*x^26 + 19*x^25 + 72*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 56*x^18 + 99*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 113*x^9 + 120*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 8*x^2 + 25*x + 40, x^29 + 106*x^27 + 36*x^26 + 75*x^25 + 36*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 108*x^18 + 107*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 57*x^9 + 124*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 52*x^2 + 17*x + 84, x^29 + 106*x^27 + 48*x^26 + 3*x^25 + 32*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 22*x^19 + 80*x^18 + 115*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + x^9 + 96*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 74*x^3 + 48*x^2 + 9*x + 96, x^29 + 106*x^27 + 80*x^26 + 19*x^25 + 16*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 112*x^18 + 35*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 113*x^9 + 112*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 16*x^2 + 89*x + 80, x^29 + 106*x^27 + 12*x^26 + 59*x^25 + 28*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 100*x^18 + 59*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 73*x^9 + 68*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 124*x^2 + 65*x + 44, x^29 + 106*x^27 + 120*x^26 + 83*x^25 + 56*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 104*x^18 + 35*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 49*x^9 + 8*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 88*x^2 + 89*x + 88, x^29 + 106*x^27 + 100*x^26 + 59*x^25 + 52*x^24 + 68*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 108*x^18 + 59*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 73*x^9 + 108*x^8 + 68*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 52*x^2 + 65*x + 100, x^29 + 106*x^27 + 20*x^26 + 107*x^25 + 20*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 124*x^18 + 11*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 25*x^9 + 12*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 36*x^2 + 113*x + 68, x^29 + 106*x^27 + 56*x^26 + 67*x^25 + 104*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 104*x^18 + 115*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 65*x^9 + 88*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 88*x^2 + 9*x + 8, x^29 + 106*x^27 + 24*x^26 + 3*x^25 + 8*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 72*x^18 + 115*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + x^9 + 56*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 120*x^2 + 9*x + 104, x^29 + 106*x^27 + 4*x^26 + 59*x^25 + 84*x^24 + 4*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 54*x^19 + 12*x^18 + 123*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 73*x^9 + 76*x^8 + 4*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 106*x^3 + 20*x^2 + x + 68, x^29 + 106*x^27 + 108*x^26 + 59*x^25 + 28*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 118*x^19 + 4*x^18 + 59*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 73*x^9 + 68*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 42*x^3 + 92*x^2 + 65*x + 44, x^29 + 106*x^27 + 104*x^26 + 3*x^25 + 24*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 22*x^19 + 56*x^18 + 115*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + x^9 + 40*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 74*x^3 + 8*x^2 + 9*x + 56, x^29 + 106*x^27 + 52*x^26 + 91*x^25 + 36*x^24 + 4*x^23 + 56*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 28*x^18 + 91*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 41*x^9 + 124*x^8 + 4*x^7 + 120*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 4*x^2 + 33*x + 84, x^29 + 106*x^27 + 72*x^26 + 19*x^25 + 72*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 24*x^18 + 35*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 113*x^9 + 120*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 40*x^2 + 89*x + 104, x^29 + 106*x^27 + 108*x^26 + 11*x^25 + 76*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 68*x^18 + 43*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 121*x^9 + 20*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 28*x^2 + 81*x + 92, x^29 + 106*x^27 + 112*x^26 + 3*x^25 + 96*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 80*x^18 + 51*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + x^9 + 32*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 48*x^2 + 73*x + 96, x^29 + 106*x^27 + 44*x^26 + 11*x^25 + 76*x^24 + 68*x^23 + 8*x^22 + 105*x^21 + 104*x^20 + 118*x^19 + 4*x^18 + 43*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 121*x^9 + 20*x^8 + 68*x^7 + 72*x^6 + 91*x^5 + 40*x^4 + 42*x^3 + 92*x^2 + 81*x + 92, x^29 + 106*x^27 + 104*x^26 + 3*x^25 + 56*x^24 + 100*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 56*x^18 + 115*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + x^9 + 8*x^8 + 100*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 8*x^2 + 9*x + 88, x^29 + 106*x^27 + 8*x^26 + 35*x^25 + 24*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 88*x^18 + 19*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 97*x^9 + 40*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 104*x^2 + 105*x + 120, x^29 + 106*x^27 + 60*x^26 + 59*x^25 + 44*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 52*x^18 + 123*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 73*x^9 + 52*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 44*x^2 + x + 60, x^29 + 106*x^27 + 68*x^26 + 107*x^25 + 4*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 76*x^18 + 75*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 25*x^9 + 28*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 84*x^2 + 49*x + 52, x^29 + 106*x^27 + 48*x^26 + 19*x^25 + 112*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 86*x^19 + 80*x^18 + 99*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 113*x^9 + 16*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 10*x^3 + 48*x^2 + 25*x + 112, x^29 + 106*x^27 + 124*x^26 + 91*x^25 + 44*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 116*x^18 + 91*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 41*x^9 + 52*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 108*x^2 + 33*x + 60, x^29 + 106*x^27 + 84*x^26 + 107*x^25 + 84*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 124*x^18 + 75*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 25*x^9 + 76*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 36*x^2 + 49*x + 68, x^29 + 106*x^27 + 76*x^26 + 75*x^25 + 108*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 100*x^18 + 107*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 84*x^10 + 57*x^9 + 116*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 124*x^2 + 17*x + 124, x^29 + 106*x^27 + 104*x^26 + 99*x^25 + 24*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 86*x^19 + 120*x^18 + 83*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 33*x^9 + 40*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 10*x^3 + 72*x^2 + 41*x + 120, x^29 + 106*x^27 + 104*x^26 + 19*x^25 + 40*x^24 + 36*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 56*x^18 + 99*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 113*x^9 + 24*x^8 + 36*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 8*x^2 + 25*x + 8, x^29 + 106*x^27 + 20*x^26 + 123*x^25 + 4*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 60*x^18 + 59*x^17 + 44*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 9*x^9 + 28*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 100*x^2 + 65*x + 52, x^29 + 106*x^27 + 16*x^26 + 19*x^25 + 16*x^24 + 36*x^23 + 32*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 112*x^18 + 99*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 113*x^9 + 112*x^8 + 36*x^7 + 32*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 16*x^2 + 25*x + 16, x^29 + 106*x^27 + 92*x^26 + 107*x^25 + 124*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 20*x^18 + 75*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 25*x^9 + 100*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 76*x^2 + 49*x + 76, x^29 + 106*x^27 + 84*x^26 + 59*x^25 + 100*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 124*x^18 + 123*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 73*x^9 + 60*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 36*x^2 + x + 20, x^29 + 106*x^27 + 8*x^26 + 83*x^25 + 72*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 22*x^19 + 88*x^18 + 99*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 49*x^9 + 120*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 74*x^3 + 104*x^2 + 25*x + 104, x^29 + 106*x^27 + 56*x^26 + 51*x^25 + 24*x^24 + 100*x^23 + 16*x^22 + 57*x^21 + 16*x^20 + 22*x^19 + 104*x^18 + 3*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 81*x^9 + 40*x^8 + 100*x^7 + 16*x^6 + 43*x^5 + 16*x^4 + 74*x^3 + 88*x^2 + 121*x + 120, x^29 + 106*x^27 + 88*x^26 + 99*x^25 + 104*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 8*x^18 + 19*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 33*x^9 + 88*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 56*x^2 + 105*x + 72, x^29 + 106*x^27 + 116*x^26 + 27*x^25 + 4*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 28*x^18 + 91*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 105*x^9 + 28*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 4*x^2 + 33*x + 116, x^29 + 106*x^27 + 76*x^26 + 91*x^25 + 124*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 100*x^18 + 91*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 41*x^9 + 100*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 124*x^2 + 33*x + 76, x^29 + 106*x^27 + 8*x^26 + 67*x^25 + 120*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 24*x^18 + 51*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 65*x^9 + 72*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 40*x^2 + 73*x + 24, x^29 + 106*x^27 + 80*x^26 + 115*x^25 + 16*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 112*x^18 + 67*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 17*x^9 + 112*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 16*x^2 + 57*x + 80, x^29 + 106*x^27 + 60*x^26 + 43*x^25 + 28*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 116*x^18 + 75*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 89*x^9 + 68*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 108*x^2 + 49*x + 44, x^29 + 106*x^27 + 36*x^26 + 27*x^25 + 52*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 44*x^18 + 91*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 105*x^9 + 108*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 116*x^2 + 33*x + 100, x^29 + 106*x^27 + 20*x^26 + 91*x^25 + 100*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 54*x^19 + 60*x^18 + 91*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 41*x^9 + 60*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 106*x^3 + 100*x^2 + 33*x + 20, x^29 + 106*x^27 + 12*x^26 + 107*x^25 + 76*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 36*x^18 + 75*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 25*x^9 + 20*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 60*x^2 + 49*x + 92, x^29 + 106*x^27 + 16*x^26 + 115*x^25 + 80*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 112*x^18 + 3*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 17*x^9 + 48*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 16*x^2 + 121*x + 80, x^29 + 106*x^27 + 8*x^26 + 99*x^25 + 56*x^24 + 36*x^23 + 112*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 88*x^18 + 83*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 33*x^9 + 8*x^8 + 36*x^7 + 112*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 104*x^2 + 41*x + 24, x^29 + 106*x^27 + 40*x^26 + 99*x^25 + 88*x^24 + 100*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 120*x^18 + 19*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 33*x^9 + 104*x^8 + 100*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 72*x^2 + 105*x + 120, x^29 + 106*x^27 + 72*x^26 + 115*x^25 + 40*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 24*x^18 + 67*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 17*x^9 + 24*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 40*x^2 + 57*x + 72, x^29 + 106*x^27 + 92*x^26 + 107*x^25 + 92*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 20*x^18 + 75*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 25*x^9 + 4*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 76*x^2 + 49*x + 44, x^29 + 106*x^27 + 72*x^26 + 67*x^25 + 24*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 24*x^18 + 115*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + 65*x^9 + 40*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 40*x^2 + 9*x + 120, x^29 + 106*x^27 + 100*x^26 + 27*x^25 + 52*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 108*x^18 + 91*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 105*x^9 + 108*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 52*x^2 + 33*x + 100, x^29 + 106*x^27 + 20*x^26 + 43*x^25 + 52*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 124*x^18 + 75*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 89*x^9 + 108*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 36*x^2 + 49*x + 100, x^29 + 106*x^27 + 120*x^26 + 67*x^25 + 72*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 104*x^18 + 51*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 65*x^9 + 120*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 88*x^2 + 73*x + 40, x^29 + 106*x^27 + 44*x^26 + 123*x^25 + 60*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 68*x^18 + 123*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 9*x^9 + 36*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 28*x^2 + x + 76, x^29 + 106*x^27 + 48*x^26 + 35*x^25 + 32*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 16*x^18 + 19*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 97*x^9 + 96*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 112*x^2 + 105*x + 32, x^29 + 106*x^27 + 44*x^26 + 107*x^25 + 44*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 104*x^20 + 54*x^19 + 68*x^18 + 11*x^17 + 36*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 25*x^9 + 52*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 40*x^4 + 106*x^3 + 28*x^2 + 113*x + 124, x^29 + 106*x^27 + 112*x^26 + 99*x^25 + 64*x^24 + 100*x^23 + 96*x^22 + 89*x^21 + 64*x^20 + 22*x^19 + 16*x^18 + 19*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 33*x^9 + 64*x^8 + 100*x^7 + 96*x^6 + 75*x^5 + 64*x^4 + 74*x^3 + 112*x^2 + 105*x, x^29 + 106*x^27 + 28*x^26 + 123*x^25 + 108*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 20*x^18 + 123*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 9*x^9 + 116*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 76*x^2 + x + 60, x^29 + 106*x^27 + 100*x^26 + 27*x^25 + 84*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 44*x^18 + 27*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 105*x^9 + 76*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 116*x^2 + 97*x + 68, x^29 + 106*x^27 + 52*x^26 + 43*x^25 + 20*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 28*x^18 + 11*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 89*x^9 + 12*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 4*x^2 + 113*x + 4, x^29 + 106*x^27 + 72*x^26 + 115*x^25 + 104*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 24*x^18 + 67*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 17*x^9 + 88*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 40*x^2 + 57*x + 8, x^29 + 106*x^27 + 28*x^26 + 43*x^25 + 124*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 84*x^18 + 11*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 89*x^9 + 100*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 12*x^2 + 113*x + 76, x^29 + 106*x^27 + 64*x^26 + 51*x^25 + 32*x^24 + 100*x^23 + 57*x^21 + 64*x^20 + 22*x^19 + 64*x^18 + 3*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 81*x^9 + 96*x^8 + 100*x^7 + 43*x^5 + 64*x^4 + 74*x^3 + 64*x^2 + 121*x + 32, x^29 + 106*x^27 + 88*x^26 + 99*x^25 + 8*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 72*x^18 + 83*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 33*x^9 + 56*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 120*x^2 + 41*x + 40, x^29 + 106*x^27 + 68*x^26 + 43*x^25 + 100*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 76*x^18 + 11*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 89*x^9 + 60*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 84*x^2 + 113*x + 20, x^29 + 106*x^27 + 4*x^26 + 75*x^25 + 68*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 76*x^18 + 43*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 57*x^9 + 92*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 84*x^2 + 81*x + 52, x^29 + 106*x^27 + 16*x^26 + 115*x^25 + 48*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 112*x^18 + 3*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 17*x^9 + 80*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 16*x^2 + 121*x + 48, x^29 + 106*x^27 + 124*x^26 + 91*x^25 + 44*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 104*x^20 + 118*x^19 + 52*x^18 + 27*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 41*x^9 + 52*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 40*x^4 + 42*x^3 + 44*x^2 + 97*x + 124, x^29 + 106*x^27 + 88*x^26 + 51*x^25 + 56*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 72*x^18 + 3*x^17 + 40*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 81*x^9 + 8*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 120*x^2 + 121*x + 24, x^29 + 106*x^27 + 80*x^26 + 3*x^25 + 36*x^23 + 96*x^22 + 89*x^21 + 86*x^19 + 112*x^18 + 51*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + x^9 + 36*x^7 + 96*x^6 + 75*x^5 + 10*x^3 + 16*x^2 + 73*x, x^29 + 106*x^27 + 104*x^26 + 35*x^25 + 120*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 120*x^18 + 19*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + 97*x^9 + 72*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 72*x^2 + 105*x + 88, x^29 + 106*x^27 + 112*x^26 + 83*x^25 + 80*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 16*x^18 + 35*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 49*x^9 + 48*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 112*x^2 + 89*x + 80, x^29 + 106*x^27 + 12*x^26 + 91*x^25 + 92*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 36*x^18 + 91*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 41*x^9 + 4*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 60*x^2 + 33*x + 44, x^29 + 106*x^27 + 16*x^26 + 3*x^25 + 32*x^24 + 100*x^23 + 32*x^22 + 25*x^21 + 22*x^19 + 112*x^18 + 115*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + x^9 + 96*x^8 + 100*x^7 + 32*x^6 + 11*x^5 + 74*x^3 + 16*x^2 + 9*x + 96, x^29 + 106*x^27 + 92*x^26 + 59*x^25 + 76*x^24 + 68*x^23 + 104*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 84*x^18 + 59*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 73*x^9 + 20*x^8 + 68*x^7 + 40*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 12*x^2 + 65*x + 28, x^29 + 106*x^27 + 96*x^26 + 99*x^25 + 48*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 32*x^20 + 86*x^19 + 32*x^18 + 83*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + 33*x^9 + 80*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 32*x^4 + 10*x^3 + 96*x^2 + 41*x + 112, x^29 + 106*x^27 + 120*x^26 + 115*x^25 + 56*x^24 + 36*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 86*x^19 + 104*x^18 + 3*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 72*x^10 + 17*x^9 + 8*x^8 + 36*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 10*x^3 + 88*x^2 + 121*x + 88, x^29 + 106*x^27 + 52*x^26 + 59*x^25 + 4*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 56*x^20 + 118*x^19 + 92*x^18 + 59*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 73*x^9 + 28*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 120*x^4 + 42*x^3 + 68*x^2 + 65*x + 116, x^29 + 106*x^27 + 28*x^26 + 27*x^25 + 108*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 54*x^19 + 84*x^18 + 27*x^17 + 36*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 105*x^9 + 116*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 106*x^3 + 12*x^2 + 97*x + 124, x^29 + 106*x^27 + 72*x^26 + 115*x^25 + 104*x^24 + 36*x^23 + 48*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 88*x^18 + 3*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 17*x^9 + 88*x^8 + 36*x^7 + 48*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 104*x^2 + 121*x + 72, x^29 + 106*x^27 + 100*x^26 + 91*x^25 + 52*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 88*x^20 + 118*x^19 + 108*x^18 + 27*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 41*x^9 + 108*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 24*x^4 + 42*x^3 + 52*x^2 + 97*x + 100, x^29 + 106*x^27 + 52*x^26 + 75*x^25 + 84*x^24 + 68*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 118*x^19 + 28*x^18 + 107*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 57*x^9 + 76*x^8 + 68*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 42*x^3 + 4*x^2 + 17*x + 68, x^29 + 106*x^27 + 36*x^26 + 75*x^25 + 36*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 44*x^18 + 43*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 57*x^9 + 124*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 116*x^2 + 81*x + 20, x^29 + 106*x^27 + 56*x^26 + 19*x^25 + 24*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 86*x^19 + 40*x^18 + 99*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 113*x^9 + 40*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 10*x^3 + 24*x^2 + 25*x + 56, x^29 + 106*x^27 + 28*x^26 + 43*x^25 + 92*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 72*x^20 + 118*x^19 + 84*x^18 + 11*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 89*x^9 + 4*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 8*x^4 + 42*x^3 + 12*x^2 + 113*x + 44, x^29 + 106*x^27 + 68*x^26 + 27*x^25 + 20*x^24 + 68*x^23 + 88*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 12*x^18 + 91*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 105*x^9 + 12*x^8 + 68*x^7 + 24*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 20*x^2 + 33*x + 68, x^29 + 106*x^27 + 24*x^26 + 99*x^25 + 40*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 86*x^19 + 8*x^18 + 83*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 33*x^9 + 24*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 10*x^3 + 56*x^2 + 41*x + 72, x^29 + 106*x^27 + 40*x^26 + 115*x^25 + 72*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 86*x^19 + 120*x^18 + 3*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 17*x^9 + 120*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 10*x^3 + 72*x^2 + 121*x + 40, x^29 + 106*x^27 + 12*x^26 + 11*x^25 + 44*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 36*x^18 + 43*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 121*x^9 + 52*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 60*x^2 + 81*x + 60, x^29 + 106*x^27 + 12*x^26 + 107*x^25 + 12*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 104*x^20 + 118*x^19 + 36*x^18 + 75*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 25*x^9 + 84*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 40*x^4 + 42*x^3 + 60*x^2 + 49*x + 28, x^29 + 106*x^27 + 60*x^26 + 123*x^25 + 76*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 116*x^18 + 123*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 9*x^9 + 20*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 108*x^2 + x + 28, x^29 + 106*x^27 + 84*x^26 + 91*x^25 + 4*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 60*x^18 + 27*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 41*x^9 + 28*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 100*x^2 + 97*x + 116, x^29 + 106*x^27 + 28*x^26 + 27*x^25 + 12*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 84*x^18 + 27*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 105*x^9 + 84*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 12*x^2 + 97*x + 28, x^29 + 106*x^27 + 12*x^26 + 43*x^25 + 44*x^24 + 68*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 36*x^18 + 11*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 89*x^9 + 52*x^8 + 68*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 60*x^2 + 113*x + 60, x^29 + 106*x^27 + 44*x^26 + 91*x^25 + 28*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 68*x^18 + 27*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 41*x^9 + 68*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 28*x^2 + 97*x + 44, x^29 + 106*x^27 + 80*x^26 + 51*x^25 + 16*x^24 + 36*x^23 + 32*x^22 + 121*x^21 + 32*x^20 + 86*x^19 + 48*x^18 + 67*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 48*x^10 + 81*x^9 + 112*x^8 + 36*x^7 + 32*x^6 + 107*x^5 + 32*x^4 + 10*x^3 + 80*x^2 + 57*x + 16, x^29 + 106*x^27 + 120*x^26 + 35*x^25 + 72*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 104*x^18 + 83*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 97*x^9 + 120*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 88*x^2 + 41*x + 40, x^29 + 106*x^27 + 8*x^26 + 67*x^25 + 88*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 88*x^18 + 115*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 65*x^9 + 104*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 104*x^2 + 9*x + 56, x^29 + 106*x^27 + 116*x^26 + 123*x^25 + 36*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 92*x^18 + 59*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 9*x^9 + 124*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 68*x^2 + 65*x + 84, x^29 + 106*x^27 + 4*x^26 + 43*x^25 + 36*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 76*x^18 + 75*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 89*x^9 + 124*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 84*x^2 + 49*x + 20, x^29 + 106*x^27 + 8*x^26 + 19*x^25 + 72*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 86*x^19 + 24*x^18 + 99*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 113*x^9 + 120*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 10*x^3 + 40*x^2 + 25*x + 40, x^29 + 106*x^27 + 16*x^26 + 51*x^25 + 80*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 48*x^18 + 3*x^17 + 112*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 81*x^9 + 48*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 80*x^2 + 121*x + 16, x^29 + 106*x^27 + 108*x^26 + 59*x^25 + 124*x^24 + 4*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 68*x^18 + 123*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 73*x^9 + 100*x^8 + 4*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 28*x^2 + x + 76, x^29 + 106*x^27 + 124*x^26 + 123*x^25 + 12*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 104*x^20 + 54*x^19 + 116*x^18 + 59*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 9*x^9 + 84*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 40*x^4 + 106*x^3 + 108*x^2 + 65*x + 28, x^29 + 106*x^27 + 48*x^26 + 99*x^25 + 32*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 16*x^18 + 83*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 33*x^9 + 96*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 112*x^2 + 41*x + 32, x^29 + 106*x^27 + 84*x^26 + 107*x^25 + 116*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 118*x^19 + 124*x^18 + 75*x^17 + 124*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 25*x^9 + 44*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 42*x^3 + 36*x^2 + 49*x + 100, x^29 + 106*x^27 + 4*x^26 + 59*x^25 + 84*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 118*x^19 + 76*x^18 + 59*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 73*x^9 + 76*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 42*x^3 + 84*x^2 + 65*x + 4, x^29 + 106*x^27 + 116*x^26 + 123*x^25 + 100*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 28*x^18 + 123*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 9*x^9 + 60*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 4*x^2 + x + 84, x^29 + 106*x^27 + 116*x^26 + 59*x^25 + 36*x^24 + 68*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 28*x^18 + 59*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 73*x^9 + 124*x^8 + 68*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 4*x^2 + 65*x + 20, x^29 + 106*x^27 + 12*x^26 + 123*x^25 + 60*x^24 + 68*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 100*x^18 + 123*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 9*x^9 + 36*x^8 + 68*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 124*x^2 + x + 76, x^29 + 106*x^27 + 60*x^26 + 27*x^25 + 76*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 52*x^18 + 27*x^17 + 68*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 105*x^9 + 20*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 44*x^2 + 97*x + 92, x^29 + 106*x^27 + 76*x^26 + 27*x^25 + 60*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 36*x^18 + 91*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 105*x^9 + 36*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 60*x^2 + 33*x + 76, x^29 + 106*x^27 + 40*x^26 + 51*x^25 + 104*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 56*x^18 + 3*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 24*x^10 + 81*x^9 + 88*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 8*x^2 + 121*x + 8, x^29 + 106*x^27 + 44*x^26 + 75*x^25 + 76*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 68*x^18 + 43*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 57*x^9 + 20*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 28*x^2 + 81*x + 28, x^29 + 106*x^27 + 96*x^26 + 19*x^25 + 96*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 22*x^19 + 32*x^18 + 35*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 113*x^9 + 32*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 74*x^3 + 96*x^2 + 89*x + 96, x^29 + 106*x^27 + 92*x^26 + 43*x^25 + 28*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 84*x^18 + 75*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 89*x^9 + 68*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 12*x^2 + 49*x + 44, x^29 + 106*x^27 + 36*x^26 + 75*x^25 + 100*x^24 + 68*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 118*x^19 + 108*x^18 + 107*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 57*x^9 + 60*x^8 + 68*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 42*x^3 + 52*x^2 + 17*x + 20, x^29 + 106*x^27 + 40*x^26 + 35*x^25 + 56*x^24 + 36*x^23 + 48*x^22 + 25*x^21 + 80*x^20 + 86*x^19 + 56*x^18 + 19*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 97*x^9 + 8*x^8 + 36*x^7 + 48*x^6 + 11*x^5 + 80*x^4 + 10*x^3 + 8*x^2 + 105*x + 24, x^29 + 106*x^27 + 100*x^26 + 27*x^25 + 20*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 44*x^18 + 27*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 105*x^9 + 12*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 116*x^2 + 97*x + 4, x^29 + 106*x^27 + 56*x^26 + 3*x^25 + 104*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 104*x^18 + 51*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + x^9 + 88*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 88*x^2 + 73*x + 8, x^29 + 106*x^27 + 88*x^26 + 67*x^25 + 72*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 72*x^18 + 115*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 65*x^9 + 120*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 120*x^2 + 9*x + 104, x^29 + 106*x^27 + 12*x^26 + 123*x^25 + 60*x^24 + 4*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 54*x^19 + 36*x^18 + 59*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 9*x^9 + 36*x^8 + 4*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 106*x^3 + 60*x^2 + 65*x + 12, x^29 + 106*x^27 + 8*x^26 + 3*x^25 + 120*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 88*x^18 + 51*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + x^9 + 72*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 104*x^2 + 73*x + 88, x^29 + 106*x^27 + 108*x^26 + 91*x^25 + 92*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 68*x^18 + 91*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 41*x^9 + 4*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 28*x^2 + 33*x + 44, x^29 + 106*x^27 + 56*x^26 + 19*x^25 + 24*x^24 + 100*x^23 + 16*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 104*x^18 + 35*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 113*x^9 + 40*x^8 + 100*x^7 + 16*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 88*x^2 + 89*x + 120, x^29 + 106*x^27 + 120*x^26 + 35*x^25 + 40*x^24 + 100*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 104*x^18 + 83*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 97*x^9 + 24*x^8 + 100*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 88*x^2 + 41*x + 8, x^29 + 106*x^27 + 88*x^26 + 35*x^25 + 8*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 22*x^19 + 8*x^18 + 83*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 97*x^9 + 56*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 74*x^3 + 56*x^2 + 41*x + 104, x^29 + 106*x^27 + 36*x^26 + 107*x^25 + 36*x^24 + 4*x^23 + 24*x^22 + 105*x^21 + 120*x^20 + 54*x^19 + 44*x^18 + 11*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 25*x^9 + 124*x^8 + 4*x^7 + 88*x^6 + 91*x^5 + 56*x^4 + 106*x^3 + 116*x^2 + 113*x + 20, x^29 + 106*x^27 + 64*x^26 + 83*x^25 + 32*x^24 + 100*x^23 + 121*x^21 + 64*x^20 + 22*x^19 + 64*x^18 + 99*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 49*x^9 + 96*x^8 + 100*x^7 + 107*x^5 + 64*x^4 + 74*x^3 + 64*x^2 + 25*x + 32, x^29 + 106*x^27 + 108*x^26 + 43*x^25 + 44*x^24 + 68*x^23 + 8*x^22 + 41*x^21 + 40*x^20 + 118*x^19 + 68*x^18 + 11*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 89*x^9 + 52*x^8 + 68*x^7 + 72*x^6 + 27*x^5 + 104*x^4 + 42*x^3 + 28*x^2 + 113*x + 60, x^29 + 106*x^27 + 96*x^26 + 19*x^25 + 96*x^24 + 36*x^23 + 57*x^21 + 86*x^19 + 96*x^18 + 99*x^17 + 96*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 113*x^9 + 32*x^8 + 36*x^7 + 43*x^5 + 10*x^3 + 32*x^2 + 25*x + 32, x^29 + 106*x^27 + 112*x^26 + 115*x^25 + 112*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 16*x^18 + 3*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 17*x^9 + 16*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 112*x^2 + 121*x + 112, x^29 + 106*x^27 + 124*x^26 + 59*x^25 + 108*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 118*x^19 + 52*x^18 + 59*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 73*x^9 + 116*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 42*x^3 + 44*x^2 + 65*x + 60, x^29 + 106*x^27 + 108*x^26 + 123*x^25 + 60*x^24 + 68*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 118*x^19 + 4*x^18 + 123*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 9*x^9 + 36*x^8 + 68*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 42*x^3 + 92*x^2 + x + 76, x^29 + 106*x^27 + 52*x^26 + 43*x^25 + 84*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 92*x^18 + 75*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 89*x^9 + 76*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 68*x^2 + 49*x + 4, x^29 + 106*x^27 + 84*x^26 + 59*x^25 + 68*x^24 + 4*x^23 + 120*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 124*x^18 + 123*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 12*x^10 + 73*x^9 + 92*x^8 + 4*x^7 + 56*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 36*x^2 + x + 116, x^29 + 106*x^27 + 68*x^26 + 75*x^25 + 68*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 12*x^18 + 43*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 57*x^9 + 92*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 20*x^2 + 81*x + 52, x^29 + 106*x^27 + 32*x^26 + 83*x^25 + 96*x^24 + 100*x^23 + 64*x^22 + 121*x^21 + 64*x^20 + 22*x^19 + 96*x^18 + 99*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 49*x^9 + 32*x^8 + 100*x^7 + 64*x^6 + 107*x^5 + 64*x^4 + 74*x^3 + 32*x^2 + 25*x + 96, x^29 + 106*x^27 + 104*x^26 + 51*x^25 + 104*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 56*x^18 + 67*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 81*x^9 + 88*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 8*x^2 + 57*x + 72, x^29 + 106*x^27 + 8*x^26 + 19*x^25 + 104*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 88*x^18 + 35*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 113*x^9 + 88*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 104*x^2 + 89*x + 8, x^29 + 106*x^27 + 8*x^26 + 115*x^25 + 40*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 88*x^18 + 67*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 17*x^9 + 24*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 104*x^2 + 57*x + 72, x^29 + 106*x^27 + 20*x^26 + 91*x^25 + 36*x^24 + 68*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 118*x^19 + 124*x^18 + 27*x^17 + 76*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 41*x^9 + 124*x^8 + 68*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 42*x^3 + 36*x^2 + 97*x + 20, x^29 + 106*x^27 + 80*x^26 + 99*x^25 + 32*x^24 + 36*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 112*x^18 + 83*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 48*x^10 + 33*x^9 + 96*x^8 + 36*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 16*x^2 + 41*x + 32, x^29 + 106*x^27 + 112*x^26 + 115*x^25 + 16*x^24 + 100*x^23 + 32*x^22 + 57*x^21 + 96*x^20 + 22*x^19 + 80*x^18 + 67*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 17*x^9 + 112*x^8 + 100*x^7 + 32*x^6 + 43*x^5 + 96*x^4 + 74*x^3 + 48*x^2 + 57*x + 80, x^29 + 106*x^27 + 104*x^26 + 83*x^25 + 40*x^24 + 100*x^23 + 48*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 120*x^18 + 99*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 49*x^9 + 24*x^8 + 100*x^7 + 48*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 72*x^2 + 25*x + 72, x^29 + 106*x^27 + 88*x^26 + 83*x^25 + 88*x^24 + 100*x^23 + 80*x^22 + 121*x^21 + 16*x^20 + 22*x^19 + 72*x^18 + 99*x^17 + 8*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 49*x^9 + 104*x^8 + 100*x^7 + 80*x^6 + 107*x^5 + 16*x^4 + 74*x^3 + 120*x^2 + 25*x + 56, x^29 + 106*x^27 + 76*x^26 + 91*x^25 + 92*x^24 + 4*x^23 + 72*x^22 + 9*x^21 + 72*x^20 + 54*x^19 + 100*x^18 + 91*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 84*x^10 + 41*x^9 + 4*x^8 + 4*x^7 + 8*x^6 + 123*x^5 + 8*x^4 + 106*x^3 + 124*x^2 + 33*x + 44, x^29 + 106*x^27 + 108*x^26 + 27*x^25 + 60*x^24 + 4*x^23 + 8*x^22 + 9*x^21 + 8*x^20 + 54*x^19 + 68*x^18 + 27*x^17 + 20*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 105*x^9 + 36*x^8 + 4*x^7 + 72*x^6 + 123*x^5 + 72*x^4 + 106*x^3 + 28*x^2 + 97*x + 12, x^29 + 106*x^27 + 24*x^26 + 3*x^25 + 72*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 72*x^18 + 115*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + x^9 + 120*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 120*x^2 + 9*x + 40, x^29 + 106*x^27 + 96*x^26 + 83*x^25 + 32*x^24 + 36*x^23 + 57*x^21 + 86*x^19 + 96*x^18 + 35*x^17 + 32*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 49*x^9 + 96*x^8 + 36*x^7 + 43*x^5 + 10*x^3 + 32*x^2 + 89*x + 96, x^29 + 106*x^27 + 12*x^26 + 27*x^25 + 28*x^24 + 68*x^23 + 8*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 100*x^18 + 91*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 20*x^10 + 105*x^9 + 68*x^8 + 68*x^7 + 72*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 124*x^2 + 33*x + 44, x^29 + 106*x^27 + 112*x^26 + 35*x^25 + 64*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 86*x^19 + 80*x^18 + 19*x^17 + 64*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 97*x^9 + 64*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 10*x^3 + 48*x^2 + 105*x + 64, x^29 + 106*x^27 + 36*x^26 + 27*x^25 + 116*x^24 + 4*x^23 + 88*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 108*x^18 + 27*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 60*x^10 + 105*x^9 + 44*x^8 + 4*x^7 + 24*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 52*x^2 + 97*x + 100, x^29 + 106*x^27 + 4*x^26 + 11*x^25 + 100*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 76*x^18 + 107*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 121*x^9 + 60*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 84*x^2 + 17*x + 84, x^29 + 106*x^27 + 124*x^26 + 43*x^25 + 124*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 116*x^18 + 11*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 89*x^9 + 100*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 108*x^2 + 113*x + 76, x^29 + 106*x^27 + 100*x^26 + 91*x^25 + 20*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 108*x^18 + 27*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 41*x^9 + 12*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 52*x^2 + 97*x + 68, x^29 + 106*x^27 + 32*x^26 + 99*x^25 + 16*x^24 + 36*x^23 + 64*x^22 + 25*x^21 + 96*x^20 + 86*x^19 + 96*x^18 + 83*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + 33*x^9 + 112*x^8 + 36*x^7 + 64*x^6 + 11*x^5 + 96*x^4 + 10*x^3 + 32*x^2 + 41*x + 80, x^29 + 106*x^27 + 124*x^26 + 91*x^25 + 12*x^24 + 4*x^23 + 104*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 116*x^18 + 91*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 41*x^9 + 84*x^8 + 4*x^7 + 40*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 108*x^2 + 33*x + 28, x^29 + 106*x^27 + 28*x^26 + 11*x^25 + 92*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 20*x^18 + 107*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 121*x^9 + 4*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 76*x^2 + 17*x + 108, x^29 + 106*x^27 + 72*x^26 + 3*x^25 + 24*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 16*x^20 + 86*x^19 + 24*x^18 + 51*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + x^9 + 40*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 16*x^4 + 10*x^3 + 40*x^2 + 73*x + 120, x^29 + 106*x^27 + 72*x^26 + 3*x^25 + 120*x^24 + 100*x^23 + 48*x^22 + 25*x^21 + 16*x^20 + 22*x^19 + 88*x^18 + 115*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 120*x^10 + x^9 + 72*x^8 + 100*x^7 + 48*x^6 + 11*x^5 + 16*x^4 + 74*x^3 + 104*x^2 + 9*x + 24, x^29 + 106*x^27 + 116*x^26 + 59*x^25 + 68*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 120*x^20 + 54*x^19 + 92*x^18 + 123*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 108*x^10 + 73*x^9 + 92*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 56*x^4 + 106*x^3 + 68*x^2 + x + 116, x^29 + 106*x^27 + 68*x^26 + 107*x^25 + 68*x^24 + 4*x^23 + 88*x^22 + 105*x^21 + 56*x^20 + 54*x^19 + 12*x^18 + 11*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 25*x^9 + 92*x^8 + 4*x^7 + 24*x^6 + 91*x^5 + 120*x^4 + 106*x^3 + 20*x^2 + 113*x + 52, x^29 + 106*x^27 + 32*x^26 + 83*x^25 + 36*x^23 + 57*x^21 + 64*x^20 + 86*x^19 + 32*x^18 + 35*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 96*x^10 + 49*x^9 + 36*x^7 + 43*x^5 + 64*x^4 + 10*x^3 + 96*x^2 + 89*x + 64, x^29 + 106*x^27 + 60*x^26 + 43*x^25 + 60*x^24 + 68*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 52*x^18 + 11*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 89*x^9 + 36*x^8 + 68*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 44*x^2 + 113*x + 12, x^29 + 106*x^27 + 4*x^26 + 59*x^25 + 116*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 76*x^18 + 59*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 73*x^9 + 44*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 84*x^2 + 65*x + 36, x^29 + 106*x^27 + 112*x^26 + 19*x^25 + 16*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 80*x^18 + 35*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 113*x^9 + 112*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 48*x^2 + 89*x + 80, x^29 + 106*x^27 + 64*x^26 + 51*x^25 + 64*x^24 + 100*x^23 + 57*x^21 + 22*x^19 + 64*x^18 + 3*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 64*x^10 + 81*x^9 + 64*x^8 + 100*x^7 + 43*x^5 + 74*x^3 + 64*x^2 + 121*x + 64, x^29 + 106*x^27 + 3*x^25 + 48*x^24 + 36*x^23 + 89*x^21 + 32*x^20 + 86*x^19 + 51*x^17 + 16*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + x^9 + 80*x^8 + 36*x^7 + 75*x^5 + 32*x^4 + 10*x^3 + 73*x + 112, x^29 + 106*x^27 + 48*x^26 + 67*x^25 + 64*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 80*x^18 + 51*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + 65*x^9 + 64*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 48*x^2 + 73*x, x^29 + 106*x^27 + 112*x^26 + 115*x^25 + 48*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 16*x^18 + 3*x^17 + 80*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 16*x^10 + 17*x^9 + 80*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 112*x^2 + 121*x + 48, x^29 + 106*x^27 + 8*x^26 + 99*x^25 + 24*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 24*x^18 + 19*x^17 + 8*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 33*x^9 + 40*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 40*x^2 + 105*x + 56, x^29 + 106*x^27 + 60*x^26 + 91*x^25 + 76*x^24 + 68*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 116*x^18 + 27*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 100*x^10 + 41*x^9 + 20*x^8 + 68*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 108*x^2 + 97*x + 28, x^29 + 106*x^27 + 8*x^26 + 115*x^25 + 8*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 88*x^18 + 67*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 17*x^9 + 56*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 104*x^2 + 57*x + 40, x^29 + 106*x^27 + 84*x^26 + 107*x^25 + 84*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 24*x^20 + 54*x^19 + 60*x^18 + 11*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 25*x^9 + 76*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 88*x^4 + 106*x^3 + 100*x^2 + 113*x + 4, x^29 + 106*x^27 + 48*x^26 + 19*x^25 + 80*x^24 + 36*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 86*x^19 + 80*x^18 + 99*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 113*x^9 + 48*x^8 + 36*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 10*x^3 + 48*x^2 + 25*x + 80, x^29 + 106*x^27 + 88*x^26 + 115*x^25 + 88*x^24 + 36*x^23 + 16*x^22 + 121*x^21 + 80*x^20 + 86*x^19 + 8*x^18 + 3*x^17 + 72*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 17*x^9 + 104*x^8 + 36*x^7 + 16*x^6 + 107*x^5 + 80*x^4 + 10*x^3 + 56*x^2 + 121*x + 120, x^29 + 106*x^27 + 8*x^26 + 83*x^25 + 104*x^24 + 36*x^23 + 48*x^22 + 57*x^21 + 48*x^20 + 86*x^19 + 24*x^18 + 35*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 49*x^9 + 88*x^8 + 36*x^7 + 48*x^6 + 43*x^5 + 48*x^4 + 10*x^3 + 40*x^2 + 89*x + 72, x^29 + 106*x^27 + 116*x^26 + 107*x^25 + 116*x^24 + 4*x^23 + 120*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 28*x^18 + 11*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 108*x^10 + 25*x^9 + 44*x^8 + 4*x^7 + 56*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 4*x^2 + 113*x + 36, x^29 + 106*x^27 + 120*x^26 + 67*x^25 + 8*x^24 + 100*x^23 + 80*x^22 + 25*x^21 + 112*x^20 + 22*x^19 + 104*x^18 + 51*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 65*x^9 + 56*x^8 + 100*x^7 + 80*x^6 + 11*x^5 + 112*x^4 + 74*x^3 + 88*x^2 + 73*x + 104, x^29 + 106*x^27 + 72*x^26 + 51*x^25 + 8*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 24*x^18 + 3*x^17 + 24*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 81*x^9 + 56*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 40*x^2 + 121*x + 40, x^29 + 106*x^27 + 8*x^26 + 83*x^25 + 40*x^24 + 100*x^23 + 112*x^22 + 121*x^21 + 112*x^20 + 22*x^19 + 88*x^18 + 99*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 56*x^10 + 49*x^9 + 24*x^8 + 100*x^7 + 112*x^6 + 107*x^5 + 112*x^4 + 74*x^3 + 104*x^2 + 25*x + 72, x^29 + 106*x^27 + 108*x^26 + 27*x^25 + 28*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 8*x^20 + 118*x^19 + 4*x^18 + 91*x^17 + 116*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 52*x^10 + 105*x^9 + 68*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 72*x^4 + 42*x^3 + 92*x^2 + 33*x + 44, x^29 + 106*x^27 + 92*x^26 + 11*x^25 + 60*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 84*x^18 + 107*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 121*x^9 + 36*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 12*x^2 + 17*x + 76, x^29 + 106*x^27 + 48*x^26 + 83*x^25 + 16*x^24 + 100*x^23 + 32*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 16*x^18 + 99*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 49*x^9 + 112*x^8 + 100*x^7 + 32*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 112*x^2 + 25*x + 80, x^29 + 106*x^27 + 100*x^26 + 43*x^25 + 4*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 44*x^18 + 11*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 89*x^9 + 28*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 116*x^2 + 113*x + 52, x^29 + 106*x^27 + 104*x^26 + 115*x^25 + 40*x^24 + 100*x^23 + 48*x^22 + 57*x^21 + 112*x^20 + 22*x^19 + 120*x^18 + 67*x^17 + 120*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 17*x^9 + 24*x^8 + 100*x^7 + 48*x^6 + 43*x^5 + 112*x^4 + 74*x^3 + 72*x^2 + 57*x + 72, x^29 + 106*x^27 + 92*x^26 + 11*x^25 + 124*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 72*x^20 + 54*x^19 + 84*x^18 + 107*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 121*x^9 + 100*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 8*x^4 + 106*x^3 + 12*x^2 + 17*x + 12, x^29 + 106*x^27 + 124*x^26 + 59*x^25 + 44*x^24 + 4*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 116*x^18 + 123*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 73*x^9 + 52*x^8 + 4*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 108*x^2 + x + 60, x^29 + 106*x^27 + 44*x^26 + 11*x^25 + 12*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 68*x^18 + 107*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 121*x^9 + 84*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 28*x^2 + 17*x + 92, x^29 + 106*x^27 + 64*x^26 + 3*x^25 + 16*x^24 + 36*x^23 + 89*x^21 + 96*x^20 + 86*x^19 + 64*x^18 + 51*x^17 + 48*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + x^9 + 112*x^8 + 36*x^7 + 75*x^5 + 96*x^4 + 10*x^3 + 64*x^2 + 73*x + 80, x^29 + 106*x^27 + 88*x^26 + 115*x^25 + 120*x^24 + 100*x^23 + 80*x^22 + 57*x^21 + 80*x^20 + 22*x^19 + 72*x^18 + 67*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 104*x^10 + 17*x^9 + 72*x^8 + 100*x^7 + 80*x^6 + 43*x^5 + 80*x^4 + 74*x^3 + 120*x^2 + 57*x + 88, x^29 + 106*x^27 + 8*x^26 + 67*x^25 + 120*x^24 + 36*x^23 + 112*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 88*x^18 + 115*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 65*x^9 + 72*x^8 + 36*x^7 + 112*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 104*x^2 + 9*x + 88, x^29 + 106*x^27 + 56*x^26 + 83*x^25 + 56*x^24 + 36*x^23 + 80*x^22 + 57*x^21 + 16*x^20 + 86*x^19 + 40*x^18 + 35*x^17 + 104*x^16 + 120*x^15 + 96*x^14 + 27*x^13 + 96*x^12 + 118*x^11 + 8*x^10 + 49*x^9 + 8*x^8 + 36*x^7 + 80*x^6 + 43*x^5 + 16*x^4 + 10*x^3 + 24*x^2 + 89*x + 88, x^29 + 106*x^27 + 96*x^26 + 3*x^25 + 80*x^24 + 36*x^23 + 64*x^22 + 89*x^21 + 96*x^20 + 86*x^19 + 32*x^18 + 51*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 32*x^10 + x^9 + 48*x^8 + 36*x^7 + 64*x^6 + 75*x^5 + 96*x^4 + 10*x^3 + 96*x^2 + 73*x + 16, x^29 + 106*x^27 + 16*x^26 + 19*x^25 + 16*x^24 + 100*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 22*x^19 + 48*x^18 + 35*x^17 + 48*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 113*x^9 + 112*x^8 + 100*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 74*x^3 + 80*x^2 + 89*x + 80, x^29 + 106*x^27 + 8*x^26 + 35*x^25 + 88*x^24 + 100*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 22*x^19 + 24*x^18 + 83*x^17 + 72*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 56*x^10 + 97*x^9 + 104*x^8 + 100*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 74*x^3 + 40*x^2 + 41*x + 120, x^29 + 106*x^27 + 28*x^26 + 11*x^25 + 92*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 84*x^18 + 43*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 4*x^10 + 121*x^9 + 4*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 12*x^2 + 81*x + 44, x^29 + 106*x^27 + 68*x^26 + 27*x^25 + 52*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 24*x^20 + 54*x^19 + 76*x^18 + 27*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 105*x^9 + 108*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 88*x^4 + 106*x^3 + 84*x^2 + 97*x + 36, x^29 + 106*x^27 + 56*x^26 + 67*x^25 + 8*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 104*x^18 + 115*x^17 + 24*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + 65*x^9 + 56*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 88*x^2 + 9*x + 40, x^29 + 106*x^27 + 64*x^26 + 35*x^25 + 80*x^24 + 36*x^23 + 25*x^21 + 96*x^20 + 86*x^19 + 64*x^18 + 19*x^17 + 112*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 64*x^10 + 97*x^9 + 48*x^8 + 36*x^7 + 11*x^5 + 96*x^4 + 10*x^3 + 64*x^2 + 105*x + 16, x^29 + 106*x^27 + 4*x^26 + 123*x^25 + 116*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 76*x^18 + 123*x^17 + 60*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 9*x^9 + 44*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 84*x^2 + x + 36, x^29 + 106*x^27 + 100*x^26 + 11*x^25 + 36*x^24 + 4*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 54*x^19 + 108*x^18 + 107*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 124*x^10 + 121*x^9 + 124*x^8 + 4*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 106*x^3 + 52*x^2 + 17*x + 20, x^29 + 106*x^27 + 44*x^26 + 27*x^25 + 60*x^24 + 68*x^23 + 72*x^22 + 73*x^21 + 72*x^20 + 118*x^19 + 68*x^18 + 91*x^17 + 84*x^16 + 56*x^15 + 48*x^14 + 123*x^13 + 48*x^12 + 54*x^11 + 116*x^10 + 105*x^9 + 36*x^8 + 68*x^7 + 8*x^6 + 59*x^5 + 8*x^4 + 42*x^3 + 28*x^2 + 33*x + 76, x^29 + 106*x^27 + 24*x^26 + 35*x^25 + 72*x^24 + 36*x^23 + 80*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 8*x^18 + 19*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 40*x^10 + 97*x^9 + 120*x^8 + 36*x^7 + 80*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 56*x^2 + 105*x + 104, x^29 + 106*x^27 + 99*x^25 + 112*x^24 + 36*x^23 + 25*x^21 + 32*x^20 + 86*x^19 + 83*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 33*x^9 + 16*x^8 + 36*x^7 + 11*x^5 + 32*x^4 + 10*x^3 + 41*x + 48, x^29 + 106*x^27 + 48*x^26 + 3*x^25 + 64*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 64*x^20 + 22*x^19 + 80*x^18 + 115*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + x^9 + 64*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 64*x^4 + 74*x^3 + 48*x^2 + 9*x, x^29 + 106*x^27 + 36*x^26 + 43*x^25 + 36*x^24 + 68*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 108*x^18 + 11*x^17 + 12*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 60*x^10 + 89*x^9 + 124*x^8 + 68*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 52*x^2 + 113*x + 84, x^29 + 106*x^27 + 12*x^26 + 75*x^25 + 44*x^24 + 68*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 118*x^19 + 36*x^18 + 107*x^17 + 100*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 20*x^10 + 57*x^9 + 52*x^8 + 68*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 42*x^3 + 60*x^2 + 17*x + 60, x^29 + 106*x^27 + 83*x^25 + 36*x^23 + 64*x^22 + 57*x^21 + 64*x^20 + 86*x^19 + 64*x^18 + 35*x^17 + 64*x^16 + 120*x^15 + 27*x^13 + 118*x^11 + 49*x^9 + 36*x^7 + 64*x^6 + 43*x^5 + 64*x^4 + 10*x^3 + 64*x^2 + 89*x + 64, x^29 + 106*x^27 + 124*x^26 + 11*x^25 + 28*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 118*x^19 + 116*x^18 + 43*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 121*x^9 + 68*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 42*x^3 + 108*x^2 + 81*x + 108, x^29 + 106*x^27 + 68*x^26 + 91*x^25 + 84*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 76*x^18 + 91*x^17 + 28*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 41*x^9 + 76*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 84*x^2 + 33*x + 68, x^29 + 106*x^27 + 108*x^26 + 75*x^25 + 12*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 4*x^18 + 43*x^17 + 68*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 57*x^9 + 84*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 92*x^2 + 81*x + 92, x^29 + 106*x^27 + 88*x^26 + 67*x^25 + 104*x^24 + 100*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 22*x^19 + 8*x^18 + 51*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 65*x^9 + 88*x^8 + 100*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 74*x^3 + 56*x^2 + 73*x + 72, x^29 + 106*x^27 + 92*x^26 + 59*x^25 + 44*x^24 + 4*x^23 + 40*x^22 + 73*x^21 + 40*x^20 + 54*x^19 + 20*x^18 + 123*x^17 + 100*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 73*x^9 + 52*x^8 + 4*x^7 + 104*x^6 + 59*x^5 + 104*x^4 + 106*x^3 + 76*x^2 + x + 60, x^29 + 106*x^27 + 120*x^26 + 99*x^25 + 72*x^24 + 36*x^23 + 16*x^22 + 25*x^21 + 48*x^20 + 86*x^19 + 40*x^18 + 83*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 33*x^9 + 120*x^8 + 36*x^7 + 16*x^6 + 11*x^5 + 48*x^4 + 10*x^3 + 24*x^2 + 41*x + 104, x^29 + 106*x^27 + 92*x^26 + 75*x^25 + 124*x^24 + 68*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 20*x^18 + 107*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 57*x^9 + 100*x^8 + 68*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 76*x^2 + 17*x + 76, x^29 + 106*x^27 + 16*x^26 + 115*x^25 + 48*x^24 + 100*x^23 + 96*x^22 + 57*x^21 + 32*x^20 + 22*x^19 + 48*x^18 + 67*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 112*x^10 + 17*x^9 + 80*x^8 + 100*x^7 + 96*x^6 + 43*x^5 + 32*x^4 + 74*x^3 + 80*x^2 + 57*x + 112, x^29 + 106*x^27 + 84*x^26 + 75*x^25 + 52*x^24 + 68*x^23 + 120*x^22 + 105*x^21 + 24*x^20 + 118*x^19 + 124*x^18 + 107*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 57*x^9 + 108*x^8 + 68*x^7 + 56*x^6 + 91*x^5 + 88*x^4 + 42*x^3 + 36*x^2 + 17*x + 36, x^29 + 106*x^27 + 120*x^26 + 67*x^25 + 40*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 112*x^20 + 86*x^19 + 40*x^18 + 115*x^17 + 120*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 72*x^10 + 65*x^9 + 24*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 112*x^4 + 10*x^3 + 24*x^2 + 9*x + 72, x^29 + 106*x^27 + 68*x^26 + 107*x^25 + 100*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 56*x^20 + 118*x^19 + 76*x^18 + 75*x^17 + 76*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 28*x^10 + 25*x^9 + 60*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 120*x^4 + 42*x^3 + 84*x^2 + 49*x + 20, x^29 + 106*x^27 + 92*x^26 + 107*x^25 + 60*x^24 + 68*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 118*x^19 + 20*x^18 + 75*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 25*x^9 + 36*x^8 + 68*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 42*x^3 + 76*x^2 + 49*x + 12, x^29 + 106*x^27 + 20*x^26 + 123*x^25 + 100*x^24 + 68*x^23 + 56*x^22 + 9*x^21 + 120*x^20 + 118*x^19 + 124*x^18 + 123*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 9*x^9 + 60*x^8 + 68*x^7 + 120*x^6 + 123*x^5 + 56*x^4 + 42*x^3 + 36*x^2 + x + 84, x^29 + 106*x^27 + 104*x^26 + 3*x^25 + 56*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 120*x^18 + 51*x^17 + 40*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 88*x^10 + x^9 + 8*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 72*x^2 + 73*x + 24, x^29 + 106*x^27 + 48*x^26 + 51*x^25 + 112*x^24 + 36*x^23 + 96*x^22 + 121*x^21 + 96*x^20 + 86*x^19 + 80*x^18 + 67*x^17 + 16*x^16 + 120*x^15 + 64*x^14 + 27*x^13 + 64*x^12 + 118*x^11 + 80*x^10 + 81*x^9 + 16*x^8 + 36*x^7 + 96*x^6 + 107*x^5 + 96*x^4 + 10*x^3 + 48*x^2 + 57*x + 112, x^29 + 106*x^27 + 124*x^26 + 107*x^25 + 124*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 52*x^18 + 11*x^17 + 20*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 25*x^9 + 100*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 44*x^2 + 113*x + 12, x^29 + 106*x^27 + 104*x^26 + 115*x^25 + 40*x^24 + 36*x^23 + 112*x^22 + 121*x^21 + 48*x^20 + 86*x^19 + 56*x^18 + 3*x^17 + 56*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 88*x^10 + 17*x^9 + 24*x^8 + 36*x^7 + 112*x^6 + 107*x^5 + 48*x^4 + 10*x^3 + 8*x^2 + 121*x + 8, x^29 + 106*x^27 + 4*x^26 + 43*x^25 + 4*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 12*x^18 + 11*x^17 + 44*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 89*x^9 + 28*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 20*x^2 + 113*x + 52, x^29 + 106*x^27 + 112*x^26 + 67*x^25 + 32*x^24 + 100*x^23 + 96*x^22 + 25*x^21 + 22*x^19 + 16*x^18 + 51*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 65*x^9 + 96*x^8 + 100*x^7 + 96*x^6 + 11*x^5 + 74*x^3 + 112*x^2 + 73*x + 96, x^29 + 106*x^27 + 88*x^26 + 35*x^25 + 40*x^24 + 100*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 22*x^19 + 8*x^18 + 83*x^17 + 56*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + 97*x^9 + 24*x^8 + 100*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 74*x^3 + 56*x^2 + 41*x + 8, x^29 + 106*x^27 + 60*x^26 + 75*x^25 + 28*x^24 + 4*x^23 + 40*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 116*x^18 + 43*x^17 + 116*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 57*x^9 + 68*x^8 + 4*x^7 + 104*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 108*x^2 + 81*x + 44, x^29 + 106*x^27 + 92*x^26 + 43*x^25 + 60*x^24 + 4*x^23 + 104*x^22 + 105*x^21 + 72*x^20 + 54*x^19 + 84*x^18 + 75*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 89*x^9 + 36*x^8 + 4*x^7 + 40*x^6 + 91*x^5 + 8*x^4 + 106*x^3 + 12*x^2 + 49*x + 76, x^29 + 106*x^27 + 96*x^26 + 19*x^25 + 64*x^24 + 36*x^23 + 57*x^21 + 64*x^20 + 86*x^19 + 96*x^18 + 99*x^17 + 120*x^15 + 27*x^13 + 118*x^11 + 32*x^10 + 113*x^9 + 64*x^8 + 36*x^7 + 43*x^5 + 64*x^4 + 10*x^3 + 32*x^2 + 25*x, x^29 + 106*x^27 + 44*x^26 + 43*x^25 + 76*x^24 + 4*x^23 + 72*x^22 + 105*x^21 + 40*x^20 + 54*x^19 + 68*x^18 + 75*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 116*x^10 + 89*x^9 + 20*x^8 + 4*x^7 + 8*x^6 + 91*x^5 + 104*x^4 + 106*x^3 + 28*x^2 + 49*x + 28, x^29 + 106*x^27 + 72*x^26 + 51*x^25 + 72*x^24 + 100*x^23 + 112*x^22 + 57*x^21 + 48*x^20 + 22*x^19 + 24*x^18 + 3*x^17 + 88*x^16 + 120*x^15 + 32*x^14 + 27*x^13 + 32*x^12 + 118*x^11 + 120*x^10 + 81*x^9 + 120*x^8 + 100*x^7 + 112*x^6 + 43*x^5 + 48*x^4 + 74*x^3 + 40*x^2 + 121*x + 104, x^29 + 106*x^27 + 4*x^26 + 107*x^25 + 68*x^24 + 68*x^23 + 24*x^22 + 41*x^21 + 120*x^20 + 118*x^19 + 12*x^18 + 75*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 25*x^9 + 92*x^8 + 68*x^7 + 88*x^6 + 27*x^5 + 56*x^4 + 42*x^3 + 20*x^2 + 49*x + 116, x^29 + 106*x^27 + 92*x^26 + 91*x^25 + 76*x^24 + 68*x^23 + 104*x^22 + 73*x^21 + 40*x^20 + 118*x^19 + 84*x^18 + 27*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 68*x^10 + 41*x^9 + 20*x^8 + 68*x^7 + 40*x^6 + 59*x^5 + 104*x^4 + 42*x^3 + 12*x^2 + 97*x + 28, x^29 + 106*x^27 + 20*x^26 + 43*x^25 + 20*x^24 + 68*x^23 + 120*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 60*x^18 + 11*x^17 + 92*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 76*x^10 + 89*x^9 + 12*x^8 + 68*x^7 + 56*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 100*x^2 + 113*x + 4, x^29 + 106*x^27 + 52*x^26 + 27*x^25 + 4*x^24 + 68*x^23 + 120*x^22 + 73*x^21 + 56*x^20 + 118*x^19 + 92*x^18 + 91*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 105*x^9 + 28*x^8 + 68*x^7 + 56*x^6 + 59*x^5 + 120*x^4 + 42*x^3 + 68*x^2 + 33*x + 116, x^29 + 106*x^27 + 84*x^26 + 107*x^25 + 116*x^24 + 4*x^23 + 56*x^22 + 105*x^21 + 88*x^20 + 54*x^19 + 60*x^18 + 11*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 25*x^9 + 44*x^8 + 4*x^7 + 120*x^6 + 91*x^5 + 24*x^4 + 106*x^3 + 100*x^2 + 113*x + 36, x^29 + 106*x^27 + 16*x^26 + 35*x^25 + 36*x^23 + 96*x^22 + 25*x^21 + 86*x^19 + 48*x^18 + 19*x^17 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 112*x^10 + 97*x^9 + 36*x^7 + 96*x^6 + 11*x^5 + 10*x^3 + 80*x^2 + 105*x, x^29 + 106*x^27 + 88*x^26 + 3*x^25 + 72*x^24 + 36*x^23 + 80*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 72*x^18 + 51*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 104*x^10 + x^9 + 120*x^8 + 36*x^7 + 80*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 120*x^2 + 73*x + 104, x^29 + 106*x^27 + 68*x^26 + 91*x^25 + 20*x^24 + 4*x^23 + 24*x^22 + 9*x^21 + 88*x^20 + 54*x^19 + 76*x^18 + 91*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 28*x^10 + 41*x^9 + 12*x^8 + 4*x^7 + 88*x^6 + 123*x^5 + 24*x^4 + 106*x^3 + 84*x^2 + 33*x + 4, x^29 + 106*x^27 + 124*x^26 + 107*x^25 + 92*x^24 + 4*x^23 + 40*x^22 + 105*x^21 + 8*x^20 + 54*x^19 + 52*x^18 + 11*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 36*x^10 + 25*x^9 + 4*x^8 + 4*x^7 + 104*x^6 + 91*x^5 + 72*x^4 + 106*x^3 + 44*x^2 + 113*x + 108, x^29 + 106*x^27 + 20*x^26 + 91*x^25 + 68*x^24 + 4*x^23 + 120*x^22 + 9*x^21 + 120*x^20 + 54*x^19 + 60*x^18 + 91*x^17 + 108*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 76*x^10 + 41*x^9 + 92*x^8 + 4*x^7 + 56*x^6 + 123*x^5 + 56*x^4 + 106*x^3 + 100*x^2 + 33*x + 116, x^29 + 106*x^27 + 60*x^26 + 11*x^25 + 124*x^24 + 68*x^23 + 104*x^22 + 105*x^21 + 8*x^20 + 118*x^19 + 52*x^18 + 43*x^17 + 84*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 100*x^10 + 121*x^9 + 100*x^8 + 68*x^7 + 40*x^6 + 91*x^5 + 72*x^4 + 42*x^3 + 44*x^2 + 81*x + 76, x^29 + 106*x^27 + 84*x^26 + 11*x^25 + 116*x^24 + 4*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 54*x^19 + 60*x^18 + 107*x^17 + 60*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 12*x^10 + 121*x^9 + 44*x^8 + 4*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 106*x^3 + 100*x^2 + 17*x + 36, x^29 + 106*x^27 + 4*x^26 + 11*x^25 + 4*x^24 + 4*x^23 + 88*x^22 + 41*x^21 + 56*x^20 + 54*x^19 + 76*x^18 + 107*x^17 + 108*x^16 + 56*x^15 + 16*x^14 + 59*x^13 + 80*x^12 + 54*x^11 + 92*x^10 + 121*x^9 + 28*x^8 + 4*x^7 + 24*x^6 + 27*x^5 + 120*x^4 + 106*x^3 + 84*x^2 + 17*x + 116, x^29 + 106*x^27 + 112*x^26 + 35*x^25 + 96*x^24 + 36*x^23 + 32*x^22 + 25*x^21 + 64*x^20 + 86*x^19 + 80*x^18 + 19*x^17 + 32*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 16*x^10 + 97*x^9 + 32*x^8 + 36*x^7 + 32*x^6 + 11*x^5 + 64*x^4 + 10*x^3 + 48*x^2 + 105*x + 96, x^29 + 106*x^27 + 28*x^26 + 91*x^25 + 12*x^24 + 4*x^23 + 40*x^22 + 9*x^21 + 104*x^20 + 54*x^19 + 84*x^18 + 91*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 4*x^10 + 41*x^9 + 84*x^8 + 4*x^7 + 104*x^6 + 123*x^5 + 40*x^4 + 106*x^3 + 12*x^2 + 33*x + 28, x^29 + 106*x^27 + 100*x^26 + 27*x^25 + 84*x^24 + 68*x^23 + 24*x^22 + 73*x^21 + 24*x^20 + 118*x^19 + 108*x^18 + 91*x^17 + 92*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 124*x^10 + 105*x^9 + 76*x^8 + 68*x^7 + 88*x^6 + 59*x^5 + 88*x^4 + 42*x^3 + 52*x^2 + 33*x + 4, x^29 + 106*x^27 + 52*x^26 + 107*x^25 + 84*x^24 + 68*x^23 + 56*x^22 + 41*x^21 + 88*x^20 + 118*x^19 + 28*x^18 + 75*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 25*x^9 + 76*x^8 + 68*x^7 + 120*x^6 + 27*x^5 + 24*x^4 + 42*x^3 + 4*x^2 + 49*x + 68, x^29 + 106*x^27 + 124*x^26 + 59*x^25 + 76*x^24 + 68*x^23 + 40*x^22 + 9*x^21 + 40*x^20 + 118*x^19 + 52*x^18 + 59*x^17 + 4*x^16 + 56*x^15 + 112*x^14 + 123*x^13 + 112*x^12 + 54*x^11 + 36*x^10 + 73*x^9 + 20*x^8 + 68*x^7 + 104*x^6 + 123*x^5 + 104*x^4 + 42*x^3 + 44*x^2 + 65*x + 28, x^29 + 106*x^27 + 4*x^26 + 123*x^25 + 52*x^24 + 68*x^23 + 88*x^22 + 9*x^21 + 88*x^20 + 118*x^19 + 76*x^18 + 123*x^17 + 124*x^16 + 56*x^15 + 16*x^14 + 123*x^13 + 16*x^12 + 54*x^11 + 92*x^10 + 9*x^9 + 108*x^8 + 68*x^7 + 24*x^6 + 123*x^5 + 24*x^4 + 42*x^3 + 84*x^2 + x + 100, x^29 + 106*x^27 + 48*x^26 + 3*x^25 + 32*x^24 + 36*x^23 + 32*x^22 + 89*x^21 + 64*x^20 + 86*x^19 + 16*x^18 + 51*x^17 + 96*x^16 + 120*x^15 + 64*x^14 + 91*x^13 + 118*x^11 + 80*x^10 + x^9 + 96*x^8 + 36*x^7 + 32*x^6 + 75*x^5 + 64*x^4 + 10*x^3 + 112*x^2 + 73*x + 32, x^29 + 106*x^27 + 32*x^26 + 3*x^25 + 48*x^24 + 100*x^23 + 25*x^21 + 96*x^20 + 22*x^19 + 32*x^18 + 115*x^17 + 80*x^16 + 120*x^15 + 91*x^13 + 64*x^12 + 118*x^11 + 96*x^10 + x^9 + 80*x^8 + 100*x^7 + 11*x^5 + 96*x^4 + 74*x^3 + 96*x^2 + 9*x + 48, x^29 + 106*x^27 + 40*x^26 + 67*x^25 + 120*x^24 + 36*x^23 + 48*x^22 + 89*x^21 + 80*x^20 + 86*x^19 + 56*x^18 + 115*x^17 + 104*x^16 + 120*x^15 + 32*x^14 + 91*x^13 + 96*x^12 + 118*x^11 + 24*x^10 + 65*x^9 + 72*x^8 + 36*x^7 + 48*x^6 + 75*x^5 + 80*x^4 + 10*x^3 + 8*x^2 + 9*x + 88, x^29 + 106*x^27 + 52*x^26 + 75*x^25 + 20*x^24 + 4*x^23 + 120*x^22 + 41*x^21 + 24*x^20 + 54*x^19 + 92*x^18 + 43*x^17 + 28*x^16 + 56*x^15 + 80*x^14 + 59*x^13 + 16*x^12 + 54*x^11 + 44*x^10 + 57*x^9 + 12*x^8 + 4*x^7 + 56*x^6 + 27*x^5 + 88*x^4 + 106*x^3 + 68*x^2 + 81*x + 68, x^29 + 106*x^27 + 92*x^26 + 11*x^25 + 92*x^24 + 4*x^23 + 104*x^22 + 41*x^21 + 8*x^20 + 54*x^19 + 84*x^18 + 107*x^17 + 52*x^16 + 56*x^15 + 112*x^14 + 59*x^13 + 48*x^12 + 54*x^11 + 68*x^10 + 121*x^9 + 4*x^8 + 4*x^7 + 40*x^6 + 27*x^5 + 72*x^4 + 106*x^3 + 12*x^2 + 17*x + 108, x^29 + 106*x^27 + 52*x^26 + 59*x^25 + 36*x^24 + 4*x^23 + 56*x^22 + 73*x^21 + 56*x^20 + 54*x^19 + 28*x^18 + 123*x^17 + 12*x^16 + 56*x^15 + 80*x^14 + 123*x^13 + 80*x^12 + 54*x^11 + 44*x^10 + 73*x^9 + 124*x^8 + 4*x^7 + 120*x^6 + 59*x^5 + 120*x^4 + 106*x^3 + 4*x^2 + x + 84, x^29 + 106*x^27 + 108*x^26 + 11*x^25 + 76*x^24 + 4*x^23 + 72*x^22 + 41*x^21 + 40*x^20 + 54*x^19 + 4*x^18 + 107*x^17 + 4*x^16 + 56*x^15 + 48*x^14 + 59*x^13 + 112*x^12 + 54*x^11 + 52*x^10 + 121*x^9 + 20*x^8 + 4*x^7 + 8*x^6 + 27*x^5 + 104*x^4 + 106*x^3 + 92*x^2 + 17*x + 28, x^29 + 106*x^27 + 56*x^26 + 3*x^25 + 72*x^24 + 36*x^23 + 16*x^22 + 89*x^21 + 48*x^20 + 86*x^19 + 104*x^18 + 51*x^17 + 88*x^16 + 120*x^15 + 96*x^14 + 91*x^13 + 32*x^12 + 118*x^11 + 8*x^10 + x^9 + 120*x^8 + 36*x^7 + 16*x^6 + 75*x^5 + 48*x^4 + 10*x^3 + 88*x^2 + 73*x + 104}


In [14]:
#precompute Seidel char polys classes n=27, e=7
#scc277=SeidelCharPolysMod(27,7)

In [15]:
scc277={x^27 + 33*x^25 + 46*x^24 + 22*x^23 + 72*x^22 + 110*x^21 + 76*x^20 + 83*x^19 + 8*x^18 + 59*x^17 + 2*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 18*x^8 + 70*x^7 + 40*x^6 + 126*x^5 + 12*x^4 + 53*x^3 + 40*x^2 + 61*x + 126, x^27 + 33*x^25 + 58*x^24 + 54*x^23 + 72*x^22 + 46*x^21 + 20*x^20 + 115*x^19 + 104*x^18 + 59*x^17 + 70*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 102*x^8 + 102*x^7 + 40*x^6 + 62*x^5 + 20*x^4 + 85*x^3 + 8*x^2 + 61*x + 90, x^27 + 33*x^25 + 66*x^24 + 38*x^23 + 72*x^22 + 62*x^21 + 100*x^20 + 67*x^19 + 104*x^18 + 107*x^17 + 62*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 94*x^8 + 22*x^7 + 40*x^6 + 14*x^5 + 100*x^4 + 101*x^3 + 8*x^2 + 45*x + 98, x^27 + 33*x^25 + 18*x^24 + 86*x^23 + 56*x^22 + 110*x^21 + 116*x^20 + 19*x^19 + 120*x^18 + 59*x^17 + 126*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 46*x^8 + 6*x^7 + 88*x^6 + 126*x^5 + 52*x^4 + 117*x^3 + 88*x^2 + 61*x + 2, x^27 + 33*x^25 + 78*x^24 + 54*x^23 + 8*x^22 + 78*x^21 + 12*x^20 + 51*x^19 + 72*x^18 + 91*x^17 + 98*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 114*x^8 + 102*x^7 + 104*x^6 + 94*x^5 + 76*x^4 + 21*x^3 + 104*x^2 + 93*x + 30, x^27 + 33*x^25 + 122*x^24 + 70*x^23 + 24*x^22 + 126*x^21 + 100*x^20 + 99*x^19 + 24*x^18 + 107*x^17 + 54*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 6*x^8 + 54*x^7 + 56*x^6 + 78*x^5 + 36*x^4 + 5*x^3 + 120*x^2 + 45*x + 10, x^27 + 33*x^25 + 34*x^24 + 86*x^23 + 56*x^22 + 46*x^21 + 20*x^20 + 19*x^19 + 120*x^18 + 123*x^17 + 110*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 30*x^8 + 6*x^7 + 88*x^6 + 62*x^5 + 84*x^4 + 117*x^3 + 88*x^2 + 125*x + 18, x^27 + 33*x^25 + 106*x^24 + 118*x^23 + 72*x^22 + 110*x^21 + 52*x^20 + 51*x^19 + 104*x^18 + 123*x^17 + 86*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 54*x^8 + 38*x^7 + 40*x^6 + 126*x^5 + 52*x^4 + 21*x^3 + 8*x^2 + 125*x + 74, x^27 + 33*x^25 + 34*x^24 + 118*x^23 + 88*x^22 + 14*x^21 + 116*x^20 + 115*x^19 + 88*x^18 + 27*x^17 + 14*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 94*x^8 + 38*x^7 + 120*x^6 + 30*x^5 + 52*x^4 + 85*x^3 + 56*x^2 + 29*x + 50, x^27 + 33*x^25 + 22*x^24 + 118*x^23 + 88*x^22 + 46*x^21 + 44*x^20 + 51*x^19 + 120*x^18 + 59*x^17 + 74*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 10*x^8 + 38*x^7 + 120*x^6 + 62*x^5 + 44*x^4 + 21*x^3 + 88*x^2 + 61*x + 86, x^27 + 33*x^25 + 102*x^24 + 54*x^23 + 24*x^22 + 110*x^21 + 76*x^20 + 115*x^19 + 56*x^18 + 123*x^17 + 122*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 58*x^8 + 102*x^7 + 56*x^6 + 126*x^5 + 76*x^4 + 85*x^3 + 24*x^2 + 125*x + 38, x^27 + 33*x^25 + 126*x^24 + 86*x^23 + 72*x^22 + 110*x^21 + 108*x^20 + 19*x^19 + 8*x^18 + 59*x^17 + 50*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 66*x^8 + 6*x^7 + 40*x^6 + 126*x^5 + 44*x^4 + 117*x^3 + 40*x^2 + 61*x + 78, x^27 + 33*x^25 + 22*x^24 + 22*x^23 + 120*x^22 + 14*x^21 + 12*x^20 + 19*x^19 + 88*x^18 + 91*x^17 + 106*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 74*x^8 + 70*x^7 + 24*x^6 + 30*x^5 + 12*x^4 + 117*x^3 + 56*x^2 + 93*x + 118, x^27 + 33*x^25 + 10*x^24 + 6*x^23 + 56*x^22 + 62*x^21 + 100*x^20 + 35*x^19 + 120*x^18 + 43*x^17 + 70*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 54*x^8 + 118*x^7 + 88*x^6 + 14*x^5 + 36*x^4 + 69*x^3 + 88*x^2 + 109*x + 58, x^27 + 33*x^25 + 46*x^24 + 22*x^23 + 104*x^22 + 46*x^21 + 44*x^20 + 83*x^19 + 104*x^18 + 123*x^17 + 34*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 82*x^8 + 70*x^7 + 72*x^6 + 62*x^5 + 108*x^4 + 53*x^3 + 8*x^2 + 125*x + 30, x^27 + 33*x^25 + 90*x^24 + 102*x^23 + 120*x^22 + 94*x^21 + 68*x^20 + 67*x^19 + 56*x^18 + 11*x^17 + 54*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 102*x^8 + 86*x^7 + 24*x^6 + 46*x^5 + 4*x^4 + 101*x^3 + 24*x^2 + 77*x + 74, x^27 + 33*x^25 + 110*x^24 + 86*x^23 + 8*x^22 + 110*x^21 + 76*x^20 + 19*x^19 + 72*x^18 + 59*x^17 + 66*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 82*x^8 + 6*x^7 + 104*x^6 + 126*x^5 + 12*x^4 + 117*x^3 + 104*x^2 + 61*x + 62, x^27 + 33*x^25 + 102*x^24 + 70*x^23 + 72*x^22 + 126*x^21 + 60*x^20 + 99*x^19 + 8*x^18 + 107*x^17 + 10*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 90*x^8 + 54*x^7 + 40*x^6 + 78*x^5 + 124*x^4 + 5*x^3 + 40*x^2 + 45*x + 118, x^27 + 33*x^25 + 90*x^24 + 86*x^23 + 8*x^22 + 78*x^21 + 20*x^20 + 83*x^19 + 40*x^18 + 27*x^17 + 102*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 70*x^8 + 6*x^7 + 104*x^6 + 94*x^5 + 20*x^4 + 53*x^3 + 72*x^2 + 29*x + 58, x^27 + 33*x^25 + 98*x^24 + 70*x^23 + 40*x^22 + 30*x^21 + 68*x^20 + 35*x^19 + 8*x^18 + 11*x^17 + 126*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 126*x^8 + 54*x^7 + 8*x^6 + 110*x^5 + 68*x^4 + 69*x^3 + 40*x^2 + 77*x + 98, x^27 + 33*x^25 + 74*x^24 + 118*x^23 + 72*x^22 + 110*x^21 + 116*x^20 + 51*x^19 + 104*x^18 + 123*x^17 + 118*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 86*x^8 + 38*x^7 + 40*x^6 + 126*x^5 + 116*x^4 + 21*x^3 + 8*x^2 + 125*x + 42, x^27 + 33*x^25 + 118*x^24 + 102*x^23 + 40*x^22 + 30*x^21 + 124*x^20 + 67*x^19 + 40*x^18 + 75*x^17 + 90*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 10*x^8 + 86*x^7 + 8*x^6 + 110*x^5 + 60*x^4 + 101*x^3 + 72*x^2 + 13*x + 102, x^27 + 33*x^25 + 74*x^24 + 70*x^23 + 56*x^22 + 126*x^21 + 100*x^20 + 99*x^19 + 120*x^18 + 107*x^17 + 6*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 118*x^8 + 54*x^7 + 88*x^6 + 78*x^5 + 36*x^4 + 5*x^3 + 88*x^2 + 45*x + 122, x^27 + 33*x^25 + 42*x^24 + 86*x^23 + 72*x^22 + 14*x^21 + 116*x^20 + 83*x^19 + 104*x^18 + 91*x^17 + 86*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 118*x^8 + 6*x^7 + 40*x^6 + 30*x^5 + 116*x^4 + 53*x^3 + 8*x^2 + 93*x + 74, x^27 + 33*x^25 + 38*x^24 + 54*x^23 + 56*x^22 + 46*x^21 + 44*x^20 + 115*x^19 + 24*x^18 + 59*x^17 + 90*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 58*x^8 + 102*x^7 + 88*x^6 + 62*x^5 + 44*x^4 + 85*x^3 + 120*x^2 + 61*x + 6, x^27 + 33*x^25 + 62*x^24 + 38*x^23 + 88*x^22 + 62*x^21 + 60*x^20 + 67*x^19 + 120*x^18 + 107*x^17 + 34*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 98*x^8 + 22*x^7 + 120*x^6 + 14*x^5 + 60*x^4 + 101*x^3 + 88*x^2 + 45*x + 126, x^27 + 33*x^25 + 86*x^24 + 38*x^23 + 104*x^22 + 94*x^21 + 124*x^20 + 3*x^19 + 104*x^18 + 11*x^17 + 58*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 42*x^8 + 22*x^7 + 72*x^6 + 46*x^5 + 60*x^4 + 37*x^3 + 8*x^2 + 77*x + 6, x^27 + 33*x^25 + 42*x^24 + 70*x^23 + 88*x^22 + 62*x^21 + 4*x^20 + 99*x^19 + 88*x^18 + 43*x^17 + 70*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 86*x^8 + 54*x^7 + 120*x^6 + 14*x^5 + 68*x^4 + 5*x^3 + 56*x^2 + 109*x + 122, x^27 + 33*x^25 + 18*x^24 + 86*x^23 + 88*x^22 + 46*x^21 + 84*x^20 + 19*x^19 + 88*x^18 + 123*x^17 + 30*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 110*x^8 + 6*x^7 + 120*x^6 + 62*x^5 + 20*x^4 + 117*x^3 + 56*x^2 + 125*x + 34, x^27 + 33*x^25 + 106*x^24 + 86*x^23 + 104*x^22 + 78*x^21 + 84*x^20 + 83*x^19 + 72*x^18 + 27*x^17 + 54*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 118*x^8 + 6*x^7 + 72*x^6 + 94*x^5 + 84*x^4 + 53*x^3 + 104*x^2 + 29*x + 42, x^27 + 33*x^25 + 102*x^24 + 38*x^23 + 104*x^22 + 94*x^21 + 92*x^20 + 3*x^19 + 104*x^18 + 11*x^17 + 106*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 26*x^8 + 22*x^7 + 72*x^6 + 46*x^5 + 28*x^4 + 37*x^3 + 8*x^2 + 77*x + 86, x^27 + 33*x^25 + 46*x^24 + 70*x^23 + 88*x^22 + 30*x^21 + 28*x^20 + 35*x^19 + 120*x^18 + 11*x^17 + 50*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 114*x^8 + 54*x^7 + 120*x^6 + 110*x^5 + 28*x^4 + 69*x^3 + 88*x^2 + 77*x + 110, x^27 + 33*x^25 + 66*x^24 + 118*x^23 + 88*x^22 + 14*x^21 + 52*x^20 + 115*x^19 + 88*x^18 + 27*x^17 + 110*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 62*x^8 + 38*x^7 + 120*x^6 + 30*x^5 + 116*x^4 + 85*x^3 + 56*x^2 + 29*x + 82, x^27 + 33*x^25 + 82*x^24 + 118*x^23 + 120*x^22 + 14*x^21 + 52*x^20 + 115*x^19 + 56*x^18 + 27*x^17 + 126*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 110*x^8 + 38*x^7 + 24*x^6 + 30*x^5 + 116*x^4 + 85*x^3 + 24*x^2 + 29*x + 2, x^27 + 33*x^25 + 2*x^24 + 118*x^23 + 24*x^22 + 14*x^21 + 116*x^20 + 115*x^19 + 24*x^18 + 27*x^17 + 110*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 126*x^8 + 38*x^7 + 56*x^6 + 30*x^5 + 52*x^4 + 85*x^3 + 120*x^2 + 29*x + 82, x^27 + 33*x^25 + 26*x^24 + 86*x^23 + 8*x^22 + 14*x^21 + 84*x^20 + 83*x^19 + 40*x^18 + 91*x^17 + 102*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 6*x^8 + 6*x^7 + 104*x^6 + 30*x^5 + 84*x^4 + 53*x^3 + 72*x^2 + 93*x + 58, x^27 + 33*x^25 + 14*x^24 + 118*x^23 + 72*x^22 + 14*x^21 + 76*x^20 + 115*x^19 + 8*x^18 + 27*x^17 + 98*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 50*x^8 + 38*x^7 + 40*x^6 + 30*x^5 + 12*x^4 + 85*x^3 + 40*x^2 + 29*x + 30, x^27 + 33*x^25 + 46*x^24 + 6*x^23 + 88*x^22 + 30*x^21 + 92*x^20 + 99*x^19 + 120*x^18 + 11*x^17 + 114*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 114*x^8 + 118*x^7 + 120*x^6 + 110*x^5 + 92*x^4 + 5*x^3 + 88*x^2 + 77*x + 46, x^27 + 33*x^25 + 38*x^24 + 38*x^23 + 40*x^22 + 30*x^21 + 92*x^20 + 3*x^19 + 40*x^18 + 75*x^17 + 42*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 90*x^8 + 22*x^7 + 8*x^6 + 110*x^5 + 28*x^4 + 37*x^3 + 72*x^2 + 13*x + 22, x^27 + 33*x^25 + 2*x^24 + 22*x^23 + 120*x^22 + 110*x^21 + 20*x^20 + 83*x^19 + 56*x^18 + 59*x^17 + 78*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 62*x^8 + 70*x^7 + 24*x^6 + 126*x^5 + 84*x^4 + 53*x^3 + 24*x^2 + 61*x + 50, x^27 + 33*x^25 + 10*x^24 + 22*x^23 + 40*x^22 + 14*x^21 + 84*x^20 + 19*x^19 + 8*x^18 + 91*x^17 + 86*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 86*x^8 + 70*x^7 + 8*x^6 + 30*x^5 + 84*x^4 + 117*x^3 + 40*x^2 + 93*x + 10, x^27 + 33*x^25 + 30*x^24 + 6*x^23 + 56*x^22 + 30*x^21 + 92*x^20 + 99*x^19 + 24*x^18 + 11*x^17 + 98*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 66*x^8 + 118*x^7 + 88*x^6 + 110*x^5 + 92*x^4 + 5*x^3 + 120*x^2 + 77*x + 126, x^27 + 33*x^25 + 18*x^24 + 38*x^23 + 8*x^22 + 62*x^21 + 4*x^20 + 67*x^19 + 40*x^18 + 107*x^17 + 110*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 14*x^8 + 22*x^7 + 104*x^6 + 14*x^5 + 4*x^4 + 101*x^3 + 72*x^2 + 45*x + 50, x^27 + 33*x^25 + 10*x^24 + 86*x^23 + 8*x^22 + 78*x^21 + 52*x^20 + 83*x^19 + 40*x^18 + 27*x^17 + 118*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 22*x^8 + 6*x^7 + 104*x^6 + 94*x^5 + 52*x^4 + 53*x^3 + 72*x^2 + 29*x + 42, x^27 + 33*x^25 + 22*x^24 + 70*x^23 + 40*x^22 + 126*x^21 + 60*x^20 + 99*x^19 + 40*x^18 + 107*x^17 + 58*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 106*x^8 + 54*x^7 + 8*x^6 + 78*x^5 + 124*x^4 + 5*x^3 + 72*x^2 + 45*x + 6, x^27 + 33*x^25 + 22*x^24 + 102*x^23 + 104*x^22 + 30*x^21 + 124*x^20 + 67*x^19 + 104*x^18 + 75*x^17 + 122*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 106*x^8 + 86*x^7 + 72*x^6 + 110*x^5 + 60*x^4 + 101*x^3 + 8*x^2 + 13*x + 70, x^27 + 33*x^25 + 74*x^24 + 6*x^23 + 120*x^22 + 126*x^21 + 100*x^20 + 35*x^19 + 56*x^18 + 107*x^17 + 6*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 118*x^8 + 118*x^7 + 24*x^6 + 78*x^5 + 36*x^4 + 69*x^3 + 24*x^2 + 45*x + 122, x^27 + 33*x^25 + 54*x^24 + 6*x^23 + 8*x^22 + 126*x^21 + 28*x^20 + 35*x^19 + 72*x^18 + 107*x^17 + 122*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 10*x^8 + 118*x^7 + 104*x^6 + 78*x^5 + 92*x^4 + 69*x^3 + 104*x^2 + 45*x + 6, x^27 + 33*x^25 + 122*x^24 + 86*x^23 + 72*x^22 + 78*x^21 + 20*x^20 + 83*x^19 + 104*x^18 + 27*x^17 + 6*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 38*x^8 + 6*x^7 + 40*x^6 + 94*x^5 + 20*x^4 + 53*x^3 + 8*x^2 + 29*x + 26, x^27 + 33*x^25 + 122*x^24 + 102*x^23 + 88*x^22 + 94*x^21 + 100*x^20 + 67*x^19 + 88*x^18 + 11*x^17 + 54*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 6*x^8 + 86*x^7 + 120*x^6 + 46*x^5 + 36*x^4 + 101*x^3 + 56*x^2 + 77*x + 10, x^27 + 33*x^25 + 38*x^24 + 6*x^23 + 104*x^22 + 126*x^21 + 28*x^20 + 35*x^19 + 104*x^18 + 107*x^17 + 106*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 90*x^8 + 118*x^7 + 72*x^6 + 78*x^5 + 92*x^4 + 69*x^3 + 8*x^2 + 45*x + 86, x^27 + 33*x^25 + 46*x^24 + 118*x^23 + 40*x^22 + 78*x^21 + 44*x^20 + 115*x^19 + 40*x^18 + 91*x^17 + 34*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 82*x^8 + 38*x^7 + 8*x^6 + 94*x^5 + 108*x^4 + 85*x^3 + 72*x^2 + 93*x + 30, x^27 + 33*x^25 + 10*x^24 + 118*x^23 + 104*x^22 + 46*x^21 + 84*x^20 + 51*x^19 + 72*x^18 + 59*x^17 + 86*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 86*x^8 + 38*x^7 + 72*x^6 + 62*x^5 + 84*x^4 + 21*x^3 + 104*x^2 + 61*x + 10, x^27 + 33*x^25 + 18*x^24 + 6*x^23 + 104*x^22 + 30*x^21 + 100*x^20 + 99*x^19 + 72*x^18 + 11*x^17 + 14*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 78*x^8 + 118*x^7 + 72*x^6 + 110*x^5 + 100*x^4 + 5*x^3 + 104*x^2 + 77*x + 82, x^27 + 33*x^25 + 46*x^24 + 70*x^23 + 24*x^22 + 30*x^21 + 92*x^20 + 35*x^19 + 56*x^18 + 11*x^17 + 114*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 114*x^8 + 54*x^7 + 56*x^6 + 110*x^5 + 92*x^4 + 69*x^3 + 24*x^2 + 77*x + 46, x^27 + 33*x^25 + 30*x^24 + 70*x^23 + 88*x^22 + 30*x^21 + 60*x^20 + 35*x^19 + 120*x^18 + 11*x^17 + 2*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 2*x^8 + 54*x^7 + 120*x^6 + 110*x^5 + 60*x^4 + 69*x^3 + 88*x^2 + 77*x + 30, x^27 + 33*x^25 + 14*x^24 + 70*x^23 + 120*x^22 + 30*x^21 + 124*x^20 + 35*x^19 + 88*x^18 + 11*x^17 + 50*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 82*x^8 + 54*x^7 + 24*x^6 + 110*x^5 + 124*x^4 + 69*x^3 + 56*x^2 + 77*x + 46, x^27 + 33*x^25 + 14*x^24 + 54*x^23 + 8*x^22 + 78*x^21 + 12*x^20 + 51*x^19 + 72*x^18 + 91*x^17 + 34*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 50*x^8 + 102*x^7 + 104*x^6 + 94*x^5 + 76*x^4 + 21*x^3 + 104*x^2 + 93*x + 94, x^27 + 33*x^25 + 42*x^24 + 22*x^23 + 40*x^22 + 14*x^21 + 20*x^20 + 19*x^19 + 8*x^18 + 91*x^17 + 54*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 54*x^8 + 70*x^7 + 8*x^6 + 30*x^5 + 20*x^4 + 117*x^3 + 40*x^2 + 93*x + 42, x^27 + 33*x^25 + 106*x^24 + 86*x^23 + 72*x^22 + 14*x^21 + 116*x^20 + 83*x^19 + 104*x^18 + 91*x^17 + 22*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 54*x^8 + 6*x^7 + 40*x^6 + 30*x^5 + 116*x^4 + 53*x^3 + 8*x^2 + 93*x + 10, x^27 + 33*x^25 + 42*x^24 + 54*x^23 + 72*x^22 + 46*x^21 + 52*x^20 + 115*x^19 + 104*x^18 + 59*x^17 + 22*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 118*x^8 + 102*x^7 + 40*x^6 + 62*x^5 + 52*x^4 + 85*x^3 + 8*x^2 + 61*x + 10, x^27 + 33*x^25 + 98*x^24 + 86*x^23 + 24*x^22 + 46*x^21 + 116*x^20 + 19*x^19 + 24*x^18 + 123*x^17 + 78*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 30*x^8 + 6*x^7 + 56*x^6 + 62*x^5 + 52*x^4 + 117*x^3 + 120*x^2 + 125*x + 114, x^27 + 33*x^25 + 50*x^24 + 22*x^23 + 24*x^22 + 46*x^21 + 20*x^20 + 83*x^19 + 24*x^18 + 123*x^17 + 126*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 78*x^8 + 70*x^7 + 56*x^6 + 62*x^5 + 84*x^4 + 53*x^3 + 120*x^2 + 125*x + 66, x^27 + 33*x^25 + 22*x^24 + 38*x^23 + 40*x^22 + 94*x^21 + 60*x^20 + 3*x^19 + 40*x^18 + 11*x^17 + 58*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 106*x^8 + 22*x^7 + 8*x^6 + 46*x^5 + 124*x^4 + 37*x^3 + 72*x^2 + 77*x + 6, x^27 + 33*x^25 + 122*x^24 + 22*x^23 + 40*x^22 + 78*x^21 + 52*x^20 + 19*x^19 + 8*x^18 + 27*x^17 + 102*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 102*x^8 + 70*x^7 + 8*x^6 + 94*x^5 + 52*x^4 + 117*x^3 + 40*x^2 + 29*x + 122, x^27 + 33*x^25 + 90*x^24 + 54*x^23 + 104*x^22 + 110*x^21 + 52*x^20 + 115*x^19 + 72*x^18 + 123*x^17 + 70*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 6*x^8 + 102*x^7 + 72*x^6 + 126*x^5 + 52*x^4 + 85*x^3 + 104*x^2 + 125*x + 26, x^27 + 33*x^25 + 58*x^24 + 118*x^23 + 72*x^22 + 46*x^21 + 84*x^20 + 51*x^19 + 104*x^18 + 59*x^17 + 6*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 102*x^8 + 38*x^7 + 40*x^6 + 62*x^5 + 84*x^4 + 21*x^3 + 8*x^2 + 61*x + 26, x^27 + 33*x^25 + 86*x^24 + 118*x^23 + 88*x^22 + 46*x^21 + 44*x^20 + 51*x^19 + 120*x^18 + 59*x^17 + 10*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 74*x^8 + 38*x^7 + 120*x^6 + 62*x^5 + 44*x^4 + 21*x^3 + 88*x^2 + 61*x + 22, x^27 + 33*x^25 + 114*x^24 + 6*x^23 + 104*x^22 + 94*x^21 + 100*x^20 + 99*x^19 + 72*x^18 + 75*x^17 + 110*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 110*x^8 + 118*x^7 + 72*x^6 + 46*x^5 + 100*x^4 + 5*x^3 + 104*x^2 + 13*x + 114, x^27 + 33*x^25 + 42*x^24 + 118*x^23 + 40*x^22 + 110*x^21 + 20*x^20 + 51*x^19 + 8*x^18 + 123*x^17 + 54*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 54*x^8 + 38*x^7 + 8*x^6 + 126*x^5 + 20*x^4 + 21*x^3 + 40*x^2 + 125*x + 42, x^27 + 33*x^25 + 46*x^24 + 38*x^23 + 120*x^22 + 62*x^21 + 124*x^20 + 67*x^19 + 88*x^18 + 107*x^17 + 82*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 50*x^8 + 22*x^7 + 24*x^6 + 14*x^5 + 124*x^4 + 101*x^3 + 56*x^2 + 45*x + 14, x^27 + 33*x^25 + 18*x^24 + 70*x^23 + 104*x^22 + 30*x^21 + 36*x^20 + 35*x^19 + 72*x^18 + 11*x^17 + 78*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 78*x^8 + 54*x^7 + 72*x^6 + 110*x^5 + 36*x^4 + 69*x^3 + 104*x^2 + 77*x + 18, x^27 + 33*x^25 + 18*x^24 + 54*x^23 + 120*x^22 + 78*x^21 + 52*x^20 + 51*x^19 + 56*x^18 + 91*x^17 + 62*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 46*x^8 + 102*x^7 + 24*x^6 + 94*x^5 + 116*x^4 + 21*x^3 + 24*x^2 + 93*x + 66, x^27 + 33*x^25 + 102*x^24 + 54*x^23 + 56*x^22 + 46*x^21 + 44*x^20 + 115*x^19 + 24*x^18 + 59*x^17 + 26*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 122*x^8 + 102*x^7 + 88*x^6 + 62*x^5 + 44*x^4 + 85*x^3 + 120*x^2 + 61*x + 70, x^27 + 33*x^25 + 114*x^24 + 22*x^23 + 24*x^22 + 46*x^21 + 20*x^20 + 83*x^19 + 24*x^18 + 123*x^17 + 62*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 14*x^8 + 70*x^7 + 56*x^6 + 62*x^5 + 84*x^4 + 53*x^3 + 120*x^2 + 125*x + 2, x^27 + 33*x^25 + 74*x^24 + 38*x^23 + 120*x^22 + 30*x^21 + 100*x^20 + 3*x^19 + 56*x^18 + 75*x^17 + 6*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 118*x^8 + 22*x^7 + 24*x^6 + 110*x^5 + 36*x^4 + 37*x^3 + 24*x^2 + 13*x + 122, x^27 + 33*x^25 + 30*x^24 + 118*x^23 + 104*x^22 + 14*x^21 + 76*x^20 + 115*x^19 + 104*x^18 + 27*x^17 + 114*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 98*x^8 + 38*x^7 + 72*x^6 + 30*x^5 + 12*x^4 + 85*x^3 + 8*x^2 + 29*x + 78, x^27 + 33*x^25 + 42*x^24 + 86*x^23 + 40*x^22 + 78*x^21 + 20*x^20 + 83*x^19 + 8*x^18 + 27*x^17 + 54*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 54*x^8 + 6*x^7 + 8*x^6 + 94*x^5 + 20*x^4 + 53*x^3 + 40*x^2 + 29*x + 42, x^27 + 33*x^25 + 86*x^24 + 86*x^23 + 56*x^22 + 14*x^21 + 12*x^20 + 83*x^19 + 24*x^18 + 91*x^17 + 42*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 10*x^8 + 6*x^7 + 88*x^6 + 30*x^5 + 12*x^4 + 53*x^3 + 120*x^2 + 93*x + 54, x^27 + 33*x^25 + 74*x^24 + 38*x^23 + 56*x^22 + 94*x^21 + 100*x^20 + 3*x^19 + 120*x^18 + 11*x^17 + 6*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 118*x^8 + 22*x^7 + 88*x^6 + 46*x^5 + 36*x^4 + 37*x^3 + 88*x^2 + 77*x + 122, x^27 + 33*x^25 + 90*x^24 + 6*x^23 + 56*x^22 + 126*x^21 + 4*x^20 + 35*x^19 + 120*x^18 + 107*x^17 + 118*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 102*x^8 + 118*x^7 + 88*x^6 + 78*x^5 + 68*x^4 + 69*x^3 + 88*x^2 + 45*x + 10, x^27 + 33*x^25 + 54*x^24 + 54*x^23 + 88*x^22 + 110*x^21 + 108*x^20 + 115*x^19 + 120*x^18 + 123*x^17 + 42*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 106*x^8 + 102*x^7 + 120*x^6 + 126*x^5 + 108*x^4 + 85*x^3 + 88*x^2 + 125*x + 118, x^27 + 33*x^25 + 54*x^24 + 22*x^23 + 88*x^22 + 14*x^21 + 44*x^20 + 19*x^19 + 120*x^18 + 91*x^17 + 106*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 106*x^8 + 70*x^7 + 120*x^6 + 30*x^5 + 44*x^4 + 117*x^3 + 88*x^2 + 93*x + 54, x^27 + 33*x^25 + 6*x^24 + 102*x^23 + 104*x^22 + 30*x^21 + 28*x^20 + 67*x^19 + 104*x^18 + 75*x^17 + 74*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 122*x^8 + 86*x^7 + 72*x^6 + 110*x^5 + 92*x^4 + 101*x^3 + 8*x^2 + 13*x + 118, x^27 + 33*x^25 + 6*x^24 + 54*x^23 + 120*x^22 + 46*x^21 + 44*x^20 + 115*x^19 + 88*x^18 + 59*x^17 + 58*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 90*x^8 + 102*x^7 + 24*x^6 + 62*x^5 + 44*x^4 + 85*x^3 + 56*x^2 + 61*x + 38, x^27 + 33*x^25 + 74*x^24 + 6*x^23 + 24*x^22 + 62*x^21 + 68*x^20 + 35*x^19 + 24*x^18 + 43*x^17 + 38*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 54*x^8 + 118*x^7 + 56*x^6 + 14*x^5 + 4*x^4 + 69*x^3 + 120*x^2 + 109*x + 26, x^27 + 33*x^25 + 54*x^24 + 6*x^23 + 104*x^22 + 62*x^21 + 60*x^20 + 35*x^19 + 104*x^18 + 43*x^17 + 90*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 74*x^8 + 118*x^7 + 72*x^6 + 14*x^5 + 124*x^4 + 69*x^3 + 8*x^2 + 109*x + 102, x^27 + 33*x^25 + 14*x^24 + 86*x^23 + 8*x^22 + 110*x^21 + 12*x^20 + 19*x^19 + 72*x^18 + 59*x^17 + 34*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 50*x^8 + 6*x^7 + 104*x^6 + 126*x^5 + 76*x^4 + 117*x^3 + 104*x^2 + 61*x + 94, x^27 + 33*x^25 + 26*x^24 + 86*x^23 + 40*x^22 + 78*x^21 + 52*x^20 + 83*x^19 + 8*x^18 + 27*x^17 + 6*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 70*x^8 + 6*x^7 + 8*x^6 + 94*x^5 + 52*x^4 + 53*x^3 + 40*x^2 + 29*x + 90, x^27 + 33*x^25 + 90*x^24 + 118*x^23 + 8*x^22 + 110*x^21 + 20*x^20 + 51*x^19 + 40*x^18 + 123*x^17 + 102*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 70*x^8 + 38*x^7 + 104*x^6 + 126*x^5 + 20*x^4 + 21*x^3 + 72*x^2 + 125*x + 58, x^27 + 33*x^25 + 106*x^24 + 86*x^23 + 8*x^22 + 14*x^21 + 52*x^20 + 83*x^19 + 40*x^18 + 91*x^17 + 86*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 54*x^8 + 6*x^7 + 104*x^6 + 30*x^5 + 52*x^4 + 53*x^3 + 72*x^2 + 93*x + 74, x^27 + 33*x^25 + 2*x^24 + 86*x^23 + 120*x^22 + 46*x^21 + 20*x^20 + 19*x^19 + 56*x^18 + 123*x^17 + 78*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 62*x^8 + 6*x^7 + 24*x^6 + 62*x^5 + 84*x^4 + 117*x^3 + 24*x^2 + 125*x + 50, x^27 + 33*x^25 + 26*x^24 + 70*x^23 + 56*x^22 + 126*x^21 + 68*x^20 + 99*x^19 + 120*x^18 + 107*x^17 + 118*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 38*x^8 + 54*x^7 + 88*x^6 + 78*x^5 + 4*x^4 + 5*x^3 + 88*x^2 + 45*x + 10, x^27 + 33*x^25 + 66*x^24 + 22*x^23 + 56*x^22 + 110*x^21 + 84*x^20 + 83*x^19 + 120*x^18 + 59*x^17 + 78*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 126*x^8 + 70*x^7 + 88*x^6 + 126*x^5 + 20*x^4 + 53*x^3 + 88*x^2 + 61*x + 50, x^27 + 33*x^25 + 86*x^24 + 38*x^23 + 40*x^22 + 30*x^21 + 124*x^20 + 3*x^19 + 40*x^18 + 75*x^17 + 58*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 42*x^8 + 22*x^7 + 8*x^6 + 110*x^5 + 60*x^4 + 37*x^3 + 72*x^2 + 13*x + 6, x^27 + 33*x^25 + 106*x^24 + 86*x^23 + 104*x^22 + 14*x^21 + 20*x^20 + 83*x^19 + 72*x^18 + 91*x^17 + 118*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 118*x^8 + 6*x^7 + 72*x^6 + 30*x^5 + 20*x^4 + 53*x^3 + 104*x^2 + 93*x + 106, x^27 + 33*x^25 + 22*x^24 + 102*x^23 + 104*x^22 + 94*x^21 + 60*x^20 + 67*x^19 + 104*x^18 + 11*x^17 + 58*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 106*x^8 + 86*x^7 + 72*x^6 + 46*x^5 + 124*x^4 + 101*x^3 + 8*x^2 + 77*x + 6, x^27 + 33*x^25 + 90*x^24 + 102*x^23 + 88*x^22 + 94*x^21 + 36*x^20 + 67*x^19 + 88*x^18 + 11*x^17 + 86*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 38*x^8 + 86*x^7 + 120*x^6 + 46*x^5 + 100*x^4 + 101*x^3 + 56*x^2 + 77*x + 106, x^27 + 33*x^25 + 6*x^24 + 54*x^23 + 88*x^22 + 110*x^21 + 76*x^20 + 115*x^19 + 120*x^18 + 123*x^17 + 26*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 26*x^8 + 102*x^7 + 120*x^6 + 126*x^5 + 76*x^4 + 85*x^3 + 88*x^2 + 125*x + 6, x^27 + 33*x^25 + 94*x^24 + 6*x^23 + 88*x^22 + 30*x^21 + 124*x^20 + 99*x^19 + 120*x^18 + 11*x^17 + 2*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 66*x^8 + 118*x^7 + 120*x^6 + 110*x^5 + 124*x^4 + 5*x^3 + 88*x^2 + 77*x + 30, x^27 + 33*x^25 + 90*x^24 + 38*x^23 + 56*x^22 + 30*x^21 + 4*x^20 + 3*x^19 + 120*x^18 + 75*x^17 + 118*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 102*x^8 + 22*x^7 + 88*x^6 + 110*x^5 + 68*x^4 + 37*x^3 + 88*x^2 + 13*x + 10, x^27 + 33*x^25 + 34*x^24 + 118*x^23 + 120*x^22 + 78*x^21 + 84*x^20 + 115*x^19 + 56*x^18 + 91*x^17 + 46*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 30*x^8 + 38*x^7 + 24*x^6 + 94*x^5 + 20*x^4 + 85*x^3 + 24*x^2 + 93*x + 82, x^27 + 33*x^25 + 26*x^24 + 54*x^23 + 72*x^22 + 46*x^21 + 84*x^20 + 115*x^19 + 104*x^18 + 59*x^17 + 102*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 6*x^8 + 102*x^7 + 40*x^6 + 62*x^5 + 84*x^4 + 85*x^3 + 8*x^2 + 61*x + 58, x^27 + 33*x^25 + 82*x^24 + 38*x^23 + 72*x^22 + 126*x^21 + 4*x^20 + 67*x^19 + 104*x^18 + 43*x^17 + 46*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 78*x^8 + 22*x^7 + 40*x^6 + 78*x^5 + 4*x^4 + 101*x^3 + 8*x^2 + 109*x + 114, x^27 + 33*x^25 + 62*x^24 + 22*x^23 + 104*x^22 + 46*x^21 + 12*x^20 + 83*x^19 + 104*x^18 + 123*x^17 + 82*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 66*x^8 + 70*x^7 + 72*x^6 + 62*x^5 + 76*x^4 + 53*x^3 + 8*x^2 + 125*x + 110, x^27 + 33*x^25 + 70*x^24 + 102*x^23 + 40*x^22 + 30*x^21 + 92*x^20 + 67*x^19 + 40*x^18 + 75*x^17 + 74*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 58*x^8 + 86*x^7 + 8*x^6 + 110*x^5 + 28*x^4 + 101*x^3 + 72*x^2 + 13*x + 118, x^27 + 33*x^25 + 110*x^24 + 118*x^23 + 40*x^22 + 78*x^21 + 44*x^20 + 115*x^19 + 40*x^18 + 91*x^17 + 98*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 18*x^8 + 38*x^7 + 8*x^6 + 94*x^5 + 108*x^4 + 85*x^3 + 72*x^2 + 93*x + 94, x^27 + 33*x^25 + 54*x^24 + 6*x^23 + 8*x^22 + 62*x^21 + 92*x^20 + 35*x^19 + 72*x^18 + 43*x^17 + 58*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 10*x^8 + 118*x^7 + 104*x^6 + 14*x^5 + 28*x^4 + 69*x^3 + 104*x^2 + 109*x + 70, x^27 + 33*x^25 + 122*x^24 + 6*x^23 + 120*x^22 + 126*x^21 + 4*x^20 + 35*x^19 + 56*x^18 + 107*x^17 + 22*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 70*x^8 + 118*x^7 + 24*x^6 + 78*x^5 + 68*x^4 + 69*x^3 + 24*x^2 + 45*x + 106, x^27 + 33*x^25 + 86*x^24 + 102*x^23 + 8*x^22 + 30*x^21 + 28*x^20 + 67*x^19 + 72*x^18 + 75*x^17 + 26*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 106*x^8 + 86*x^7 + 104*x^6 + 110*x^5 + 92*x^4 + 101*x^3 + 104*x^2 + 13*x + 102, x^27 + 33*x^25 + 106*x^24 + 102*x^23 + 56*x^22 + 30*x^21 + 36*x^20 + 67*x^19 + 120*x^18 + 75*x^17 + 102*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 86*x^8 + 86*x^7 + 88*x^6 + 110*x^5 + 100*x^4 + 101*x^3 + 88*x^2 + 13*x + 26, x^27 + 33*x^25 + 10*x^24 + 38*x^23 + 120*x^22 + 94*x^21 + 36*x^20 + 3*x^19 + 56*x^18 + 11*x^17 + 6*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 54*x^8 + 22*x^7 + 24*x^6 + 46*x^5 + 100*x^4 + 37*x^3 + 24*x^2 + 77*x + 122, x^27 + 33*x^25 + 74*x^24 + 102*x^23 + 88*x^22 + 94*x^21 + 68*x^20 + 67*x^19 + 88*x^18 + 11*x^17 + 38*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 54*x^8 + 86*x^7 + 120*x^6 + 46*x^5 + 4*x^4 + 101*x^3 + 56*x^2 + 77*x + 26, x^27 + 33*x^25 + 102*x^24 + 38*x^23 + 8*x^22 + 94*x^21 + 124*x^20 + 3*x^19 + 72*x^18 + 11*x^17 + 74*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 90*x^8 + 22*x^7 + 104*x^6 + 46*x^5 + 60*x^4 + 37*x^3 + 104*x^2 + 77*x + 54, x^27 + 33*x^25 + 14*x^24 + 38*x^23 + 24*x^22 + 126*x^21 + 28*x^20 + 67*x^19 + 56*x^18 + 43*x^17 + 18*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 18*x^8 + 22*x^7 + 56*x^6 + 78*x^5 + 28*x^4 + 101*x^3 + 24*x^2 + 109*x + 14, x^27 + 33*x^25 + 42*x^24 + 70*x^23 + 88*x^22 + 126*x^21 + 68*x^20 + 99*x^19 + 88*x^18 + 107*x^17 + 6*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 86*x^8 + 54*x^7 + 120*x^6 + 78*x^5 + 4*x^4 + 5*x^3 + 56*x^2 + 45*x + 58, x^27 + 33*x^25 + 122*x^24 + 38*x^23 + 88*x^22 + 30*x^21 + 100*x^20 + 3*x^19 + 88*x^18 + 75*x^17 + 54*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 6*x^8 + 22*x^7 + 120*x^6 + 110*x^5 + 36*x^4 + 37*x^3 + 56*x^2 + 13*x + 10, x^27 + 33*x^25 + 118*x^24 + 70*x^23 + 104*x^22 + 62*x^21 + 124*x^20 + 99*x^19 + 104*x^18 + 43*x^17 + 90*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 10*x^8 + 54*x^7 + 72*x^6 + 14*x^5 + 60*x^4 + 5*x^3 + 8*x^2 + 109*x + 102, x^27 + 33*x^25 + 94*x^24 + 70*x^23 + 120*x^22 + 30*x^21 + 92*x^20 + 35*x^19 + 88*x^18 + 11*x^17 + 34*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 2*x^8 + 54*x^7 + 24*x^6 + 110*x^5 + 92*x^4 + 69*x^3 + 56*x^2 + 77*x + 62, x^27 + 33*x^25 + 82*x^24 + 22*x^23 + 24*x^22 + 46*x^21 + 84*x^20 + 83*x^19 + 24*x^18 + 123*x^17 + 94*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 46*x^8 + 70*x^7 + 56*x^6 + 62*x^5 + 20*x^4 + 53*x^3 + 120*x^2 + 125*x + 98, x^27 + 33*x^25 + 102*x^24 + 102*x^23 + 72*x^22 + 94*x^21 + 124*x^20 + 67*x^19 + 8*x^18 + 11*x^17 + 74*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 90*x^8 + 86*x^7 + 40*x^6 + 46*x^5 + 60*x^4 + 101*x^3 + 40*x^2 + 77*x + 54, x^27 + 33*x^25 + 106*x^24 + 118*x^23 + 104*x^22 + 110*x^21 + 84*x^20 + 51*x^19 + 72*x^18 + 123*x^17 + 54*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 118*x^8 + 38*x^7 + 72*x^6 + 126*x^5 + 84*x^4 + 21*x^3 + 104*x^2 + 125*x + 42, x^27 + 33*x^25 + 38*x^24 + 54*x^23 + 56*x^22 + 110*x^21 + 108*x^20 + 115*x^19 + 24*x^18 + 123*x^17 + 26*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 58*x^8 + 102*x^7 + 88*x^6 + 126*x^5 + 108*x^4 + 85*x^3 + 120*x^2 + 125*x + 70, x^27 + 33*x^25 + 122*x^24 + 54*x^23 + 72*x^22 + 46*x^21 + 20*x^20 + 115*x^19 + 104*x^18 + 59*x^17 + 6*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 38*x^8 + 102*x^7 + 40*x^6 + 62*x^5 + 20*x^4 + 85*x^3 + 8*x^2 + 61*x + 26, x^27 + 33*x^25 + 18*x^24 + 54*x^23 + 56*x^22 + 78*x^21 + 116*x^20 + 51*x^19 + 120*x^18 + 91*x^17 + 126*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 46*x^8 + 102*x^7 + 88*x^6 + 94*x^5 + 52*x^4 + 21*x^3 + 88*x^2 + 93*x + 2, x^27 + 33*x^25 + 14*x^24 + 54*x^23 + 40*x^22 + 78*x^21 + 44*x^20 + 51*x^19 + 40*x^18 + 91*x^17 + 2*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 114*x^8 + 102*x^7 + 8*x^6 + 94*x^5 + 108*x^4 + 21*x^3 + 72*x^2 + 93*x + 62, x^27 + 33*x^25 + 114*x^24 + 102*x^23 + 72*x^22 + 126*x^21 + 4*x^20 + 3*x^19 + 104*x^18 + 43*x^17 + 78*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 46*x^8 + 86*x^7 + 40*x^6 + 78*x^5 + 4*x^4 + 37*x^3 + 8*x^2 + 109*x + 82, x^27 + 33*x^25 + 118*x^24 + 6*x^23 + 40*x^22 + 62*x^21 + 124*x^20 + 35*x^19 + 40*x^18 + 43*x^17 + 90*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 10*x^8 + 118*x^7 + 8*x^6 + 14*x^5 + 60*x^4 + 69*x^3 + 72*x^2 + 109*x + 102, x^27 + 33*x^25 + 106*x^24 + 54*x^23 + 40*x^22 + 110*x^21 + 84*x^20 + 115*x^19 + 8*x^18 + 123*x^17 + 54*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 118*x^8 + 102*x^7 + 8*x^6 + 126*x^5 + 84*x^4 + 85*x^3 + 40*x^2 + 125*x + 42, x^27 + 33*x^25 + 38*x^24 + 70*x^23 + 104*x^22 + 126*x^21 + 92*x^20 + 99*x^19 + 104*x^18 + 107*x^17 + 42*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 90*x^8 + 54*x^7 + 72*x^6 + 78*x^5 + 28*x^4 + 5*x^3 + 8*x^2 + 45*x + 22, x^27 + 33*x^25 + 74*x^24 + 118*x^23 + 8*x^22 + 46*x^21 + 116*x^20 + 51*x^19 + 40*x^18 + 59*x^17 + 118*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 86*x^8 + 38*x^7 + 104*x^6 + 62*x^5 + 116*x^4 + 21*x^3 + 72*x^2 + 61*x + 42, x^27 + 33*x^25 + 70*x^24 + 70*x^23 + 72*x^22 + 126*x^21 + 124*x^20 + 99*x^19 + 8*x^18 + 107*x^17 + 42*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 122*x^8 + 54*x^7 + 40*x^6 + 78*x^5 + 60*x^4 + 5*x^3 + 40*x^2 + 45*x + 86, x^27 + 33*x^25 + 122*x^24 + 54*x^23 + 104*x^22 + 46*x^21 + 52*x^20 + 115*x^19 + 72*x^18 + 59*x^17 + 102*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 102*x^8 + 102*x^7 + 72*x^6 + 62*x^5 + 52*x^4 + 85*x^3 + 104*x^2 + 61*x + 122, x^27 + 33*x^25 + 78*x^24 + 102*x^23 + 120*x^22 + 126*x^21 + 60*x^20 + 3*x^19 + 88*x^18 + 43*x^17 + 50*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 18*x^8 + 86*x^7 + 24*x^6 + 78*x^5 + 60*x^4 + 37*x^3 + 56*x^2 + 109*x + 46, x^27 + 33*x^25 + 114*x^24 + 38*x^23 + 104*x^22 + 126*x^21 + 100*x^20 + 67*x^19 + 72*x^18 + 43*x^17 + 110*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 110*x^8 + 22*x^7 + 72*x^6 + 78*x^5 + 100*x^4 + 101*x^3 + 104*x^2 + 109*x + 114, x^27 + 33*x^25 + 54*x^24 + 118*x^23 + 24*x^22 + 46*x^21 + 44*x^20 + 51*x^19 + 56*x^18 + 59*x^17 + 106*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 106*x^8 + 38*x^7 + 56*x^6 + 62*x^5 + 44*x^4 + 21*x^3 + 24*x^2 + 61*x + 54, x^27 + 33*x^25 + 6*x^24 + 6*x^23 + 72*x^22 + 126*x^21 + 60*x^20 + 35*x^19 + 8*x^18 + 107*x^17 + 42*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 58*x^8 + 118*x^7 + 40*x^6 + 78*x^5 + 124*x^4 + 69*x^3 + 40*x^2 + 45*x + 86, x^27 + 33*x^25 + 118*x^24 + 38*x^23 + 104*x^22 + 30*x^21 + 124*x^20 + 3*x^19 + 104*x^18 + 75*x^17 + 90*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 10*x^8 + 22*x^7 + 72*x^6 + 110*x^5 + 60*x^4 + 37*x^3 + 8*x^2 + 13*x + 102, x^27 + 33*x^25 + 114*x^24 + 102*x^23 + 104*x^22 + 62*x^21 + 100*x^20 + 3*x^19 + 72*x^18 + 107*x^17 + 110*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 110*x^8 + 86*x^7 + 72*x^6 + 14*x^5 + 100*x^4 + 37*x^3 + 104*x^2 + 45*x + 114, x^27 + 33*x^25 + 118*x^24 + 38*x^23 + 40*x^22 + 30*x^21 + 60*x^20 + 3*x^19 + 40*x^18 + 75*x^17 + 26*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 10*x^8 + 22*x^7 + 8*x^6 + 110*x^5 + 124*x^4 + 37*x^3 + 72*x^2 + 13*x + 38, x^27 + 33*x^25 + 18*x^24 + 6*x^23 + 8*x^22 + 30*x^21 + 4*x^20 + 99*x^19 + 40*x^18 + 11*x^17 + 110*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 14*x^8 + 118*x^7 + 104*x^6 + 110*x^5 + 4*x^4 + 5*x^3 + 72*x^2 + 77*x + 50, x^27 + 33*x^25 + 66*x^24 + 22*x^23 + 56*x^22 + 46*x^21 + 20*x^20 + 83*x^19 + 120*x^18 + 123*x^17 + 14*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 126*x^8 + 70*x^7 + 88*x^6 + 62*x^5 + 84*x^4 + 53*x^3 + 88*x^2 + 125*x + 114, x^27 + 33*x^25 + 106*x^24 + 6*x^23 + 120*x^22 + 126*x^21 + 36*x^20 + 35*x^19 + 56*x^18 + 107*x^17 + 102*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 86*x^8 + 118*x^7 + 24*x^6 + 78*x^5 + 100*x^4 + 69*x^3 + 24*x^2 + 45*x + 26, x^27 + 33*x^25 + 74*x^24 + 22*x^23 + 40*x^22 + 78*x^21 + 20*x^20 + 19*x^19 + 8*x^18 + 27*x^17 + 86*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 22*x^8 + 70*x^7 + 8*x^6 + 94*x^5 + 20*x^4 + 117*x^3 + 40*x^2 + 29*x + 10, x^27 + 33*x^25 + 42*x^24 + 6*x^23 + 56*x^22 + 62*x^21 + 36*x^20 + 35*x^19 + 120*x^18 + 43*x^17 + 38*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 22*x^8 + 118*x^7 + 88*x^6 + 14*x^5 + 100*x^4 + 69*x^3 + 88*x^2 + 109*x + 90, x^27 + 33*x^25 + 2*x^24 + 70*x^23 + 8*x^22 + 94*x^21 + 36*x^20 + 35*x^19 + 40*x^18 + 75*x^17 + 62*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 30*x^8 + 54*x^7 + 104*x^6 + 46*x^5 + 36*x^4 + 69*x^3 + 72*x^2 + 13*x + 98, x^27 + 33*x^25 + 102*x^24 + 118*x^23 + 24*x^22 + 110*x^21 + 12*x^20 + 51*x^19 + 56*x^18 + 123*x^17 + 58*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 58*x^8 + 38*x^7 + 56*x^6 + 126*x^5 + 12*x^4 + 21*x^3 + 24*x^2 + 125*x + 102, x^27 + 33*x^25 + 70*x^24 + 70*x^23 + 40*x^22 + 62*x^21 + 28*x^20 + 99*x^19 + 40*x^18 + 43*x^17 + 10*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 58*x^8 + 54*x^7 + 8*x^6 + 14*x^5 + 92*x^4 + 5*x^3 + 72*x^2 + 109*x + 54, x^27 + 33*x^25 + 14*x^24 + 38*x^23 + 24*x^22 + 62*x^21 + 92*x^20 + 67*x^19 + 56*x^18 + 107*x^17 + 82*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 18*x^8 + 22*x^7 + 56*x^6 + 14*x^5 + 92*x^4 + 101*x^3 + 24*x^2 + 45*x + 78, x^27 + 33*x^25 + 110*x^24 + 86*x^23 + 40*x^22 + 46*x^21 + 44*x^20 + 19*x^19 + 40*x^18 + 123*x^17 + 98*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 18*x^8 + 6*x^7 + 8*x^6 + 62*x^5 + 108*x^4 + 117*x^3 + 72*x^2 + 125*x + 94, x^27 + 33*x^25 + 122*x^24 + 6*x^23 + 56*x^22 + 62*x^21 + 4*x^20 + 35*x^19 + 120*x^18 + 43*x^17 + 22*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 70*x^8 + 118*x^7 + 88*x^6 + 14*x^5 + 68*x^4 + 69*x^3 + 88*x^2 + 109*x + 106, x^27 + 33*x^25 + 6*x^24 + 86*x^23 + 88*x^22 + 78*x^21 + 12*x^20 + 83*x^19 + 120*x^18 + 27*x^17 + 90*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 26*x^8 + 6*x^7 + 120*x^6 + 94*x^5 + 12*x^4 + 53*x^3 + 88*x^2 + 29*x + 70, x^27 + 33*x^25 + 54*x^24 + 102*x^23 + 72*x^22 + 94*x^21 + 92*x^20 + 67*x^19 + 8*x^18 + 11*x^17 + 58*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 10*x^8 + 86*x^7 + 40*x^6 + 46*x^5 + 28*x^4 + 101*x^3 + 40*x^2 + 77*x + 70, x^27 + 33*x^25 + 106*x^24 + 6*x^23 + 24*x^22 + 62*x^21 + 4*x^20 + 35*x^19 + 24*x^18 + 43*x^17 + 6*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 22*x^8 + 118*x^7 + 56*x^6 + 14*x^5 + 68*x^4 + 69*x^3 + 120*x^2 + 109*x + 58, x^27 + 33*x^25 + 94*x^24 + 86*x^23 + 72*x^22 + 110*x^21 + 44*x^20 + 19*x^19 + 8*x^18 + 59*x^17 + 82*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 98*x^8 + 6*x^7 + 40*x^6 + 126*x^5 + 108*x^4 + 117*x^3 + 40*x^2 + 61*x + 46, x^27 + 33*x^25 + 58*x^24 + 6*x^23 + 24*x^22 + 126*x^21 + 36*x^20 + 35*x^19 + 24*x^18 + 107*x^17 + 54*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 70*x^8 + 118*x^7 + 56*x^6 + 78*x^5 + 100*x^4 + 69*x^3 + 120*x^2 + 45*x + 10, x^27 + 33*x^25 + 62*x^24 + 54*x^23 + 40*x^22 + 14*x^21 + 12*x^20 + 51*x^19 + 40*x^18 + 27*x^17 + 82*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 66*x^8 + 102*x^7 + 8*x^6 + 30*x^5 + 76*x^4 + 21*x^3 + 72*x^2 + 29*x + 110, x^27 + 33*x^25 + 30*x^24 + 22*x^23 + 72*x^22 + 46*x^21 + 44*x^20 + 83*x^19 + 8*x^18 + 123*x^17 + 18*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 34*x^8 + 70*x^7 + 40*x^6 + 62*x^5 + 108*x^4 + 53*x^3 + 40*x^2 + 125*x + 110, x^27 + 33*x^25 + 86*x^24 + 54*x^23 + 56*x^22 + 46*x^21 + 76*x^20 + 115*x^19 + 24*x^18 + 59*x^17 + 106*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 10*x^8 + 102*x^7 + 88*x^6 + 62*x^5 + 76*x^4 + 85*x^3 + 120*x^2 + 61*x + 118, x^27 + 33*x^25 + 18*x^24 + 70*x^23 + 40*x^22 + 30*x^21 + 100*x^20 + 35*x^19 + 8*x^18 + 11*x^17 + 14*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 78*x^8 + 54*x^7 + 8*x^6 + 110*x^5 + 100*x^4 + 69*x^3 + 40*x^2 + 77*x + 82, x^27 + 33*x^25 + 18*x^24 + 6*x^23 + 8*x^22 + 94*x^21 + 68*x^20 + 99*x^19 + 40*x^18 + 75*x^17 + 46*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 14*x^8 + 118*x^7 + 104*x^6 + 46*x^5 + 68*x^4 + 5*x^3 + 72*x^2 + 13*x + 114, x^27 + 33*x^25 + 26*x^24 + 6*x^23 + 120*x^22 + 126*x^21 + 68*x^20 + 35*x^19 + 56*x^18 + 107*x^17 + 118*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 38*x^8 + 118*x^7 + 24*x^6 + 78*x^5 + 4*x^4 + 69*x^3 + 24*x^2 + 45*x + 10, x^27 + 33*x^25 + 2*x^24 + 38*x^23 + 104*x^22 + 62*x^21 + 4*x^20 + 67*x^19 + 72*x^18 + 107*x^17 + 94*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 94*x^8 + 22*x^7 + 72*x^6 + 14*x^5 + 4*x^4 + 101*x^3 + 104*x^2 + 45*x + 2, x^27 + 33*x^25 + 74*x^24 + 54*x^23 + 104*x^22 + 110*x^21 + 84*x^20 + 115*x^19 + 72*x^18 + 123*x^17 + 22*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 22*x^8 + 102*x^7 + 72*x^6 + 126*x^5 + 84*x^4 + 85*x^3 + 104*x^2 + 125*x + 74, x^27 + 33*x^25 + 50*x^24 + 86*x^23 + 88*x^22 + 110*x^21 + 84*x^20 + 19*x^19 + 88*x^18 + 59*x^17 + 62*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 78*x^8 + 6*x^7 + 120*x^6 + 126*x^5 + 20*x^4 + 117*x^3 + 56*x^2 + 61*x + 2, x^27 + 33*x^25 + 118*x^24 + 86*x^23 + 56*x^22 + 14*x^21 + 76*x^20 + 83*x^19 + 24*x^18 + 91*x^17 + 10*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 106*x^8 + 6*x^7 + 88*x^6 + 30*x^5 + 76*x^4 + 53*x^3 + 120*x^2 + 93*x + 86, x^27 + 33*x^25 + 34*x^24 + 102*x^23 + 104*x^22 + 62*x^21 + 4*x^20 + 3*x^19 + 72*x^18 + 107*x^17 + 126*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 62*x^8 + 86*x^7 + 72*x^6 + 14*x^5 + 4*x^4 + 37*x^3 + 104*x^2 + 45*x + 98, x^27 + 33*x^25 + 26*x^24 + 54*x^23 + 72*x^22 + 110*x^21 + 20*x^20 + 115*x^19 + 104*x^18 + 123*x^17 + 38*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 6*x^8 + 102*x^7 + 40*x^6 + 126*x^5 + 20*x^4 + 85*x^3 + 8*x^2 + 125*x + 122, x^27 + 33*x^25 + 110*x^24 + 118*x^23 + 104*x^22 + 14*x^21 + 44*x^20 + 115*x^19 + 104*x^18 + 27*x^17 + 98*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 18*x^8 + 38*x^7 + 72*x^6 + 30*x^5 + 108*x^4 + 85*x^3 + 8*x^2 + 29*x + 94, x^27 + 33*x^25 + 90*x^24 + 102*x^23 + 120*x^22 + 30*x^21 + 4*x^20 + 67*x^19 + 56*x^18 + 75*x^17 + 118*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 102*x^8 + 86*x^7 + 24*x^6 + 110*x^5 + 68*x^4 + 101*x^3 + 24*x^2 + 13*x + 10, x^27 + 33*x^25 + 10*x^24 + 38*x^23 + 120*x^22 + 30*x^21 + 100*x^20 + 3*x^19 + 56*x^18 + 75*x^17 + 70*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 54*x^8 + 22*x^7 + 24*x^6 + 110*x^5 + 36*x^4 + 37*x^3 + 24*x^2 + 13*x + 58, x^27 + 33*x^25 + 42*x^24 + 102*x^23 + 56*x^22 + 94*x^21 + 100*x^20 + 67*x^19 + 120*x^18 + 11*x^17 + 102*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 22*x^8 + 86*x^7 + 88*x^6 + 46*x^5 + 36*x^4 + 101*x^3 + 88*x^2 + 77*x + 26, x^27 + 33*x^25 + 78*x^24 + 102*x^23 + 24*x^22 + 126*x^21 + 92*x^20 + 3*x^19 + 56*x^18 + 43*x^17 + 18*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 82*x^8 + 86*x^7 + 56*x^6 + 78*x^5 + 92*x^4 + 37*x^3 + 24*x^2 + 109*x + 14, x^27 + 33*x^25 + 102*x^24 + 102*x^23 + 72*x^22 + 30*x^21 + 60*x^20 + 67*x^19 + 8*x^18 + 75*x^17 + 10*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 90*x^8 + 86*x^7 + 40*x^6 + 110*x^5 + 124*x^4 + 101*x^3 + 40*x^2 + 13*x + 118, x^27 + 33*x^25 + 94*x^24 + 54*x^23 + 104*x^22 + 78*x^21 + 76*x^20 + 51*x^19 + 104*x^18 + 91*x^17 + 50*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 34*x^8 + 102*x^7 + 72*x^6 + 94*x^5 + 12*x^4 + 21*x^3 + 8*x^2 + 93*x + 14, x^27 + 33*x^25 + 118*x^24 + 70*x^23 + 104*x^22 + 126*x^21 + 60*x^20 + 99*x^19 + 104*x^18 + 107*x^17 + 26*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 10*x^8 + 54*x^7 + 72*x^6 + 78*x^5 + 124*x^4 + 5*x^3 + 8*x^2 + 45*x + 38, x^27 + 33*x^25 + 34*x^24 + 22*x^23 + 120*x^22 + 46*x^21 + 20*x^20 + 83*x^19 + 56*x^18 + 123*x^17 + 110*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 30*x^8 + 70*x^7 + 24*x^6 + 62*x^5 + 84*x^4 + 53*x^3 + 24*x^2 + 125*x + 18, x^27 + 33*x^25 + 102*x^24 + 86*x^23 + 120*x^22 + 14*x^21 + 44*x^20 + 83*x^19 + 88*x^18 + 91*x^17 + 26*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 122*x^8 + 6*x^7 + 24*x^6 + 30*x^5 + 44*x^4 + 53*x^3 + 56*x^2 + 93*x + 70, x^27 + 33*x^25 + 10*x^24 + 22*x^23 + 72*x^22 + 14*x^21 + 116*x^20 + 19*x^19 + 104*x^18 + 91*x^17 + 54*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 22*x^8 + 70*x^7 + 40*x^6 + 30*x^5 + 116*x^4 + 117*x^3 + 8*x^2 + 93*x + 106, x^27 + 33*x^25 + 62*x^24 + 102*x^23 + 120*x^22 + 62*x^21 + 28*x^20 + 3*x^19 + 88*x^18 + 107*x^17 + 66*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 34*x^8 + 86*x^7 + 24*x^6 + 14*x^5 + 28*x^4 + 37*x^3 + 56*x^2 + 45*x + 30, x^27 + 33*x^25 + 10*x^24 + 6*x^23 + 56*x^22 + 126*x^21 + 36*x^20 + 35*x^19 + 120*x^18 + 107*x^17 + 6*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 54*x^8 + 118*x^7 + 88*x^6 + 78*x^5 + 100*x^4 + 69*x^3 + 88*x^2 + 45*x + 122, x^27 + 33*x^25 + 46*x^24 + 102*x^23 + 120*x^22 + 126*x^21 + 124*x^20 + 3*x^19 + 88*x^18 + 43*x^17 + 82*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 50*x^8 + 86*x^7 + 24*x^6 + 78*x^5 + 124*x^4 + 37*x^3 + 56*x^2 + 109*x + 14, x^27 + 33*x^25 + 50*x^24 + 6*x^23 + 8*x^22 + 94*x^21 + 4*x^20 + 99*x^19 + 40*x^18 + 75*x^17 + 14*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 110*x^8 + 118*x^7 + 104*x^6 + 46*x^5 + 4*x^4 + 5*x^3 + 72*x^2 + 13*x + 18, x^27 + 33*x^25 + 58*x^24 + 6*x^23 + 120*x^22 + 126*x^21 + 4*x^20 + 35*x^19 + 56*x^18 + 107*x^17 + 86*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 6*x^8 + 118*x^7 + 24*x^6 + 78*x^5 + 68*x^4 + 69*x^3 + 24*x^2 + 45*x + 42, x^27 + 33*x^25 + 46*x^24 + 70*x^23 + 88*x^22 + 94*x^21 + 92*x^20 + 35*x^19 + 120*x^18 + 75*x^17 + 114*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 114*x^8 + 54*x^7 + 120*x^6 + 46*x^5 + 92*x^4 + 69*x^3 + 88*x^2 + 13*x + 46, x^27 + 33*x^25 + 22*x^24 + 54*x^23 + 120*x^22 + 46*x^21 + 12*x^20 + 115*x^19 + 88*x^18 + 59*x^17 + 106*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 74*x^8 + 102*x^7 + 24*x^6 + 62*x^5 + 12*x^4 + 85*x^3 + 56*x^2 + 61*x + 118, x^27 + 33*x^25 + 6*x^24 + 86*x^23 + 56*x^22 + 14*x^21 + 44*x^20 + 83*x^19 + 24*x^18 + 91*x^17 + 58*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 90*x^8 + 6*x^7 + 88*x^6 + 30*x^5 + 44*x^4 + 53*x^3 + 120*x^2 + 93*x + 38, x^27 + 33*x^25 + 70*x^24 + 70*x^23 + 8*x^22 + 126*x^21 + 60*x^20 + 99*x^19 + 72*x^18 + 107*x^17 + 106*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 122*x^8 + 54*x^7 + 104*x^6 + 78*x^5 + 124*x^4 + 5*x^3 + 104*x^2 + 45*x + 22, x^27 + 33*x^25 + 26*x^24 + 6*x^23 + 88*x^22 + 126*x^21 + 36*x^20 + 35*x^19 + 88*x^18 + 107*x^17 + 22*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 102*x^8 + 118*x^7 + 120*x^6 + 78*x^5 + 100*x^4 + 69*x^3 + 56*x^2 + 45*x + 42, x^27 + 33*x^25 + 58*x^24 + 118*x^23 + 40*x^22 + 46*x^21 + 52*x^20 + 51*x^19 + 8*x^18 + 59*x^17 + 38*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 38*x^8 + 38*x^7 + 8*x^6 + 62*x^5 + 52*x^4 + 21*x^3 + 40*x^2 + 61*x + 58, x^27 + 33*x^25 + 26*x^24 + 86*x^23 + 72*x^22 + 78*x^21 + 84*x^20 + 83*x^19 + 104*x^18 + 27*x^17 + 102*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 6*x^8 + 6*x^7 + 40*x^6 + 94*x^5 + 84*x^4 + 53*x^3 + 8*x^2 + 29*x + 58, x^27 + 33*x^25 + 34*x^24 + 102*x^23 + 8*x^22 + 62*x^21 + 36*x^20 + 3*x^19 + 40*x^18 + 107*x^17 + 94*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 126*x^8 + 86*x^7 + 104*x^6 + 14*x^5 + 36*x^4 + 37*x^3 + 72*x^2 + 45*x + 66, x^27 + 33*x^25 + 110*x^24 + 86*x^23 + 104*x^22 + 46*x^21 + 108*x^20 + 19*x^19 + 104*x^18 + 123*x^17 + 34*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 18*x^8 + 6*x^7 + 72*x^6 + 62*x^5 + 44*x^4 + 117*x^3 + 8*x^2 + 125*x + 30, x^27 + 33*x^25 + 118*x^24 + 54*x^23 + 120*x^22 + 46*x^21 + 76*x^20 + 115*x^19 + 88*x^18 + 59*x^17 + 10*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 106*x^8 + 102*x^7 + 24*x^6 + 62*x^5 + 76*x^4 + 85*x^3 + 56*x^2 + 61*x + 86, x^27 + 33*x^25 + 34*x^24 + 6*x^23 + 8*x^22 + 30*x^21 + 100*x^20 + 99*x^19 + 40*x^18 + 11*x^17 + 30*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 126*x^8 + 118*x^7 + 104*x^6 + 110*x^5 + 100*x^4 + 5*x^3 + 72*x^2 + 77*x + 2, x^27 + 33*x^25 + 66*x^24 + 86*x^23 + 88*x^22 + 46*x^21 + 116*x^20 + 19*x^19 + 88*x^18 + 123*x^17 + 46*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 62*x^8 + 6*x^7 + 120*x^6 + 62*x^5 + 52*x^4 + 117*x^3 + 56*x^2 + 125*x + 18, x^27 + 33*x^25 + 82*x^24 + 22*x^23 + 88*x^22 + 110*x^21 + 84*x^20 + 83*x^19 + 88*x^18 + 59*x^17 + 94*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 46*x^8 + 70*x^7 + 120*x^6 + 126*x^5 + 20*x^4 + 53*x^3 + 56*x^2 + 61*x + 98, x^27 + 33*x^25 + 46*x^24 + 102*x^23 + 56*x^22 + 126*x^21 + 60*x^20 + 3*x^19 + 24*x^18 + 43*x^17 + 18*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 50*x^8 + 86*x^7 + 88*x^6 + 78*x^5 + 60*x^4 + 37*x^3 + 120*x^2 + 109*x + 78, x^27 + 33*x^25 + 118*x^24 + 38*x^23 + 72*x^22 + 30*x^21 + 92*x^20 + 3*x^19 + 8*x^18 + 75*x^17 + 122*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 74*x^8 + 22*x^7 + 40*x^6 + 110*x^5 + 28*x^4 + 37*x^3 + 40*x^2 + 13*x + 6, x^27 + 33*x^25 + 50*x^24 + 54*x^23 + 120*x^22 + 14*x^21 + 52*x^20 + 51*x^19 + 56*x^18 + 27*x^17 + 94*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 14*x^8 + 102*x^7 + 24*x^6 + 30*x^5 + 116*x^4 + 21*x^3 + 24*x^2 + 29*x + 34, x^27 + 33*x^25 + 6*x^24 + 102*x^23 + 40*x^22 + 30*x^21 + 92*x^20 + 67*x^19 + 40*x^18 + 75*x^17 + 10*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 122*x^8 + 86*x^7 + 8*x^6 + 110*x^5 + 28*x^4 + 101*x^3 + 72*x^2 + 13*x + 54, x^27 + 33*x^25 + 42*x^24 + 6*x^23 + 24*x^22 + 62*x^21 + 4*x^20 + 35*x^19 + 24*x^18 + 43*x^17 + 70*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 86*x^8 + 118*x^7 + 56*x^6 + 14*x^5 + 68*x^4 + 69*x^3 + 120*x^2 + 109*x + 122, x^27 + 33*x^25 + 30*x^24 + 22*x^23 + 72*x^22 + 110*x^21 + 108*x^20 + 83*x^19 + 8*x^18 + 59*x^17 + 82*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 34*x^8 + 70*x^7 + 40*x^6 + 126*x^5 + 44*x^4 + 53*x^3 + 40*x^2 + 61*x + 46, x^27 + 33*x^25 + 66*x^24 + 54*x^23 + 24*x^22 + 14*x^21 + 52*x^20 + 51*x^19 + 24*x^18 + 27*x^17 + 110*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 62*x^8 + 102*x^7 + 56*x^6 + 30*x^5 + 116*x^4 + 21*x^3 + 120*x^2 + 29*x + 82, x^27 + 33*x^25 + 18*x^24 + 54*x^23 + 120*x^22 + 14*x^21 + 116*x^20 + 51*x^19 + 56*x^18 + 27*x^17 + 126*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 46*x^8 + 102*x^7 + 24*x^6 + 30*x^5 + 52*x^4 + 21*x^3 + 24*x^2 + 29*x + 2, x^27 + 33*x^25 + 106*x^24 + 86*x^23 + 8*x^22 + 78*x^21 + 116*x^20 + 83*x^19 + 40*x^18 + 27*x^17 + 22*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 54*x^8 + 6*x^7 + 104*x^6 + 94*x^5 + 116*x^4 + 53*x^3 + 72*x^2 + 29*x + 10, x^27 + 33*x^25 + 98*x^24 + 38*x^23 + 8*x^22 + 62*x^21 + 100*x^20 + 67*x^19 + 40*x^18 + 107*x^17 + 94*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 62*x^8 + 22*x^7 + 104*x^6 + 14*x^5 + 100*x^4 + 101*x^3 + 72*x^2 + 45*x + 66, x^27 + 33*x^25 + 70*x^24 + 38*x^23 + 40*x^22 + 30*x^21 + 28*x^20 + 3*x^19 + 40*x^18 + 75*x^17 + 10*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 58*x^8 + 22*x^7 + 8*x^6 + 110*x^5 + 92*x^4 + 37*x^3 + 72*x^2 + 13*x + 54, x^27 + 33*x^25 + 66*x^24 + 38*x^23 + 8*x^22 + 62*x^21 + 36*x^20 + 67*x^19 + 40*x^18 + 107*x^17 + 126*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 94*x^8 + 22*x^7 + 104*x^6 + 14*x^5 + 36*x^4 + 101*x^3 + 72*x^2 + 45*x + 34, x^27 + 33*x^25 + 10*x^24 + 22*x^23 + 104*x^22 + 78*x^21 + 84*x^20 + 19*x^19 + 72*x^18 + 27*x^17 + 86*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 86*x^8 + 70*x^7 + 72*x^6 + 94*x^5 + 84*x^4 + 117*x^3 + 104*x^2 + 29*x + 10, x^27 + 33*x^25 + 62*x^24 + 102*x^23 + 56*x^22 + 62*x^21 + 92*x^20 + 3*x^19 + 24*x^18 + 107*x^17 + 2*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 34*x^8 + 86*x^7 + 88*x^6 + 14*x^5 + 92*x^4 + 37*x^3 + 120*x^2 + 45*x + 94, x^27 + 33*x^25 + 98*x^24 + 54*x^23 + 24*x^22 + 78*x^21 + 52*x^20 + 51*x^19 + 24*x^18 + 91*x^17 + 14*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 30*x^8 + 102*x^7 + 56*x^6 + 94*x^5 + 116*x^4 + 21*x^3 + 120*x^2 + 93*x + 50, x^27 + 33*x^25 + 74*x^24 + 86*x^23 + 104*x^22 + 14*x^21 + 84*x^20 + 83*x^19 + 72*x^18 + 91*x^17 + 22*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 22*x^8 + 6*x^7 + 72*x^6 + 30*x^5 + 84*x^4 + 53*x^3 + 104*x^2 + 93*x + 74, x^27 + 33*x^25 + 58*x^24 + 54*x^23 + 40*x^22 + 46*x^21 + 116*x^20 + 115*x^19 + 8*x^18 + 59*x^17 + 102*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 38*x^8 + 102*x^7 + 8*x^6 + 62*x^5 + 116*x^4 + 85*x^3 + 40*x^2 + 61*x + 122, x^27 + 33*x^25 + 94*x^24 + 38*x^23 + 88*x^22 + 126*x^21 + 60*x^20 + 67*x^19 + 120*x^18 + 43*x^17 + 66*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 66*x^8 + 22*x^7 + 120*x^6 + 78*x^5 + 60*x^4 + 101*x^3 + 88*x^2 + 109*x + 94, x^27 + 33*x^25 + 2*x^24 + 6*x^23 + 104*x^22 + 94*x^21 + 68*x^20 + 99*x^19 + 72*x^18 + 75*x^17 + 30*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 94*x^8 + 118*x^7 + 72*x^6 + 46*x^5 + 68*x^4 + 5*x^3 + 104*x^2 + 13*x + 66, x^27 + 33*x^25 + 50*x^24 + 102*x^23 + 40*x^22 + 62*x^21 + 36*x^20 + 3*x^19 + 8*x^18 + 107*x^17 + 110*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 46*x^8 + 86*x^7 + 8*x^6 + 14*x^5 + 36*x^4 + 37*x^3 + 40*x^2 + 45*x + 114, x^27 + 33*x^25 + 6*x^24 + 102*x^23 + 40*x^22 + 94*x^21 + 28*x^20 + 67*x^19 + 40*x^18 + 11*x^17 + 74*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 122*x^8 + 86*x^7 + 8*x^6 + 46*x^5 + 92*x^4 + 101*x^3 + 72*x^2 + 77*x + 118, x^27 + 33*x^25 + 126*x^24 + 22*x^23 + 72*x^22 + 46*x^21 + 108*x^20 + 83*x^19 + 8*x^18 + 123*x^17 + 50*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 66*x^8 + 70*x^7 + 40*x^6 + 62*x^5 + 44*x^4 + 53*x^3 + 40*x^2 + 125*x + 78, x^27 + 33*x^25 + 78*x^24 + 38*x^23 + 56*x^22 + 62*x^21 + 124*x^20 + 67*x^19 + 24*x^18 + 107*x^17 + 114*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 18*x^8 + 22*x^7 + 88*x^6 + 14*x^5 + 124*x^4 + 101*x^3 + 120*x^2 + 45*x + 110, x^27 + 33*x^25 + 2*x^24 + 38*x^23 + 72*x^22 + 126*x^21 + 36*x^20 + 67*x^19 + 104*x^18 + 43*x^17 + 62*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 30*x^8 + 22*x^7 + 40*x^6 + 78*x^5 + 36*x^4 + 101*x^3 + 8*x^2 + 109*x + 98, x^27 + 33*x^25 + 106*x^24 + 54*x^23 + 72*x^22 + 46*x^21 + 52*x^20 + 115*x^19 + 104*x^18 + 59*x^17 + 86*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 54*x^8 + 102*x^7 + 40*x^6 + 62*x^5 + 52*x^4 + 85*x^3 + 8*x^2 + 61*x + 74, x^27 + 33*x^25 + 18*x^24 + 102*x^23 + 8*x^22 + 62*x^21 + 68*x^20 + 3*x^19 + 40*x^18 + 107*x^17 + 46*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 14*x^8 + 86*x^7 + 104*x^6 + 14*x^5 + 68*x^4 + 37*x^3 + 72*x^2 + 45*x + 114, x^27 + 33*x^25 + 114*x^24 + 22*x^23 + 56*x^22 + 110*x^21 + 116*x^20 + 83*x^19 + 120*x^18 + 59*x^17 + 94*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 78*x^8 + 70*x^7 + 88*x^6 + 126*x^5 + 52*x^4 + 53*x^3 + 88*x^2 + 61*x + 34, x^27 + 33*x^25 + 90*x^24 + 6*x^23 + 24*x^22 + 126*x^21 + 100*x^20 + 35*x^19 + 24*x^18 + 107*x^17 + 22*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 38*x^8 + 118*x^7 + 56*x^6 + 78*x^5 + 36*x^4 + 69*x^3 + 120*x^2 + 45*x + 42, x^27 + 33*x^25 + 14*x^24 + 86*x^23 + 104*x^22 + 46*x^21 + 44*x^20 + 19*x^19 + 104*x^18 + 123*x^17 + 2*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 114*x^8 + 6*x^7 + 72*x^6 + 62*x^5 + 108*x^4 + 117*x^3 + 8*x^2 + 125*x + 62, x^27 + 33*x^25 + 106*x^24 + 102*x^23 + 88*x^22 + 30*x^21 + 68*x^20 + 67*x^19 + 88*x^18 + 75*x^17 + 70*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 22*x^8 + 86*x^7 + 120*x^6 + 110*x^5 + 4*x^4 + 101*x^3 + 56*x^2 + 13*x + 122, x^27 + 33*x^25 + 42*x^24 + 118*x^23 + 104*x^22 + 110*x^21 + 84*x^20 + 51*x^19 + 72*x^18 + 123*x^17 + 118*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 54*x^8 + 38*x^7 + 72*x^6 + 126*x^5 + 84*x^4 + 21*x^3 + 104*x^2 + 125*x + 106, x^27 + 33*x^25 + 114*x^24 + 6*x^23 + 8*x^22 + 94*x^21 + 4*x^20 + 99*x^19 + 40*x^18 + 75*x^17 + 78*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 46*x^8 + 118*x^7 + 104*x^6 + 46*x^5 + 4*x^4 + 5*x^3 + 72*x^2 + 13*x + 82, x^27 + 33*x^25 + 34*x^24 + 22*x^23 + 56*x^22 + 46*x^21 + 84*x^20 + 83*x^19 + 120*x^18 + 123*x^17 + 46*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 30*x^8 + 70*x^7 + 88*x^6 + 62*x^5 + 20*x^4 + 53*x^3 + 88*x^2 + 125*x + 82, x^27 + 33*x^25 + 126*x^24 + 102*x^23 + 120*x^22 + 62*x^21 + 28*x^20 + 3*x^19 + 88*x^18 + 107*x^17 + 2*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 98*x^8 + 86*x^7 + 24*x^6 + 14*x^5 + 28*x^4 + 37*x^3 + 56*x^2 + 45*x + 94, x^27 + 33*x^25 + 122*x^24 + 38*x^23 + 24*x^22 + 94*x^21 + 100*x^20 + 3*x^19 + 24*x^18 + 11*x^17 + 54*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 6*x^8 + 22*x^7 + 56*x^6 + 46*x^5 + 36*x^4 + 37*x^3 + 120*x^2 + 77*x + 10, x^27 + 33*x^25 + 70*x^24 + 6*x^23 + 104*x^22 + 62*x^21 + 28*x^20 + 35*x^19 + 104*x^18 + 43*x^17 + 10*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 58*x^8 + 118*x^7 + 72*x^6 + 14*x^5 + 92*x^4 + 69*x^3 + 8*x^2 + 109*x + 54, x^27 + 33*x^25 + 22*x^24 + 118*x^23 + 56*x^22 + 46*x^21 + 12*x^20 + 51*x^19 + 24*x^18 + 59*x^17 + 106*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 74*x^8 + 38*x^7 + 88*x^6 + 62*x^5 + 12*x^4 + 21*x^3 + 120*x^2 + 61*x + 118, x^27 + 33*x^25 + 86*x^24 + 6*x^23 + 8*x^22 + 126*x^21 + 92*x^20 + 35*x^19 + 72*x^18 + 107*x^17 + 90*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 106*x^8 + 118*x^7 + 104*x^6 + 78*x^5 + 28*x^4 + 69*x^3 + 104*x^2 + 45*x + 38, x^27 + 33*x^25 + 66*x^24 + 38*x^23 + 8*x^22 + 126*x^21 + 100*x^20 + 67*x^19 + 40*x^18 + 43*x^17 + 62*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 94*x^8 + 22*x^7 + 104*x^6 + 78*x^5 + 100*x^4 + 101*x^3 + 72*x^2 + 109*x + 98, x^27 + 33*x^25 + 46*x^24 + 22*x^23 + 40*x^22 + 110*x^21 + 44*x^20 + 83*x^19 + 40*x^18 + 59*x^17 + 34*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 82*x^8 + 70*x^7 + 8*x^6 + 126*x^5 + 108*x^4 + 53*x^3 + 72*x^2 + 61*x + 30, x^27 + 33*x^25 + 90*x^24 + 70*x^23 + 88*x^22 + 62*x^21 + 36*x^20 + 99*x^19 + 88*x^18 + 43*x^17 + 86*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 38*x^8 + 54*x^7 + 120*x^6 + 14*x^5 + 100*x^4 + 5*x^3 + 56*x^2 + 109*x + 106, x^27 + 33*x^25 + 26*x^24 + 22*x^23 + 104*x^22 + 78*x^21 + 52*x^20 + 19*x^19 + 72*x^18 + 27*x^17 + 6*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 70*x^8 + 70*x^7 + 72*x^6 + 94*x^5 + 52*x^4 + 117*x^3 + 104*x^2 + 29*x + 90, x^27 + 33*x^25 + 90*x^24 + 86*x^23 + 72*x^22 + 78*x^21 + 84*x^20 + 83*x^19 + 104*x^18 + 27*x^17 + 38*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 70*x^8 + 6*x^7 + 40*x^6 + 94*x^5 + 84*x^4 + 53*x^3 + 8*x^2 + 29*x + 122, x^27 + 33*x^25 + 106*x^24 + 6*x^23 + 56*x^22 + 62*x^21 + 36*x^20 + 35*x^19 + 120*x^18 + 43*x^17 + 102*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 86*x^8 + 118*x^7 + 88*x^6 + 14*x^5 + 100*x^4 + 69*x^3 + 88*x^2 + 109*x + 26, x^27 + 33*x^25 + 54*x^24 + 86*x^23 + 120*x^22 + 78*x^21 + 76*x^20 + 83*x^19 + 88*x^18 + 27*x^17 + 74*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 42*x^8 + 6*x^7 + 24*x^6 + 94*x^5 + 76*x^4 + 53*x^3 + 56*x^2 + 29*x + 22, x^27 + 33*x^25 + 114*x^24 + 22*x^23 + 120*x^22 + 46*x^21 + 116*x^20 + 83*x^19 + 56*x^18 + 123*x^17 + 94*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 78*x^8 + 70*x^7 + 24*x^6 + 62*x^5 + 52*x^4 + 53*x^3 + 24*x^2 + 125*x + 34, x^27 + 33*x^25 + 126*x^24 + 54*x^23 + 72*x^22 + 78*x^21 + 108*x^20 + 51*x^19 + 8*x^18 + 91*x^17 + 50*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 66*x^8 + 102*x^7 + 40*x^6 + 94*x^5 + 44*x^4 + 21*x^3 + 40*x^2 + 93*x + 78, x^27 + 33*x^25 + 74*x^24 + 54*x^23 + 40*x^22 + 46*x^21 + 84*x^20 + 115*x^19 + 8*x^18 + 59*x^17 + 22*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 22*x^8 + 102*x^7 + 8*x^6 + 62*x^5 + 84*x^4 + 85*x^3 + 40*x^2 + 61*x + 74, x^27 + 33*x^25 + 6*x^24 + 54*x^23 + 88*x^22 + 46*x^21 + 12*x^20 + 115*x^19 + 120*x^18 + 59*x^17 + 90*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 26*x^8 + 102*x^7 + 120*x^6 + 62*x^5 + 12*x^4 + 85*x^3 + 88*x^2 + 61*x + 70, x^27 + 33*x^25 + 58*x^24 + 38*x^23 + 120*x^22 + 94*x^21 + 68*x^20 + 3*x^19 + 56*x^18 + 11*x^17 + 22*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 6*x^8 + 22*x^7 + 24*x^6 + 46*x^5 + 4*x^4 + 37*x^3 + 24*x^2 + 77*x + 106, x^27 + 33*x^25 + 82*x^24 + 86*x^23 + 88*x^22 + 46*x^21 + 84*x^20 + 19*x^19 + 88*x^18 + 123*x^17 + 94*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 46*x^8 + 6*x^7 + 120*x^6 + 62*x^5 + 20*x^4 + 117*x^3 + 56*x^2 + 125*x + 98, x^27 + 33*x^25 + 78*x^24 + 118*x^23 + 8*x^22 + 14*x^21 + 12*x^20 + 115*x^19 + 72*x^18 + 27*x^17 + 98*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 114*x^8 + 38*x^7 + 104*x^6 + 30*x^5 + 76*x^4 + 85*x^3 + 104*x^2 + 29*x + 30, x^27 + 33*x^25 + 122*x^24 + 54*x^23 + 8*x^22 + 110*x^21 + 20*x^20 + 115*x^19 + 40*x^18 + 123*x^17 + 6*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 38*x^8 + 102*x^7 + 104*x^6 + 126*x^5 + 20*x^4 + 85*x^3 + 72*x^2 + 125*x + 26, x^27 + 33*x^25 + 62*x^24 + 22*x^23 + 40*x^22 + 110*x^21 + 12*x^20 + 83*x^19 + 40*x^18 + 59*x^17 + 82*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 66*x^8 + 70*x^7 + 8*x^6 + 126*x^5 + 76*x^4 + 53*x^3 + 72*x^2 + 61*x + 110, x^27 + 33*x^25 + 82*x^24 + 102*x^23 + 104*x^22 + 126*x^21 + 100*x^20 + 3*x^19 + 72*x^18 + 43*x^17 + 78*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 14*x^8 + 86*x^7 + 72*x^6 + 78*x^5 + 100*x^4 + 37*x^3 + 104*x^2 + 109*x + 18, x^27 + 33*x^25 + 10*x^24 + 118*x^23 + 40*x^22 + 110*x^21 + 84*x^20 + 51*x^19 + 8*x^18 + 123*x^17 + 86*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 86*x^8 + 38*x^7 + 8*x^6 + 126*x^5 + 84*x^4 + 21*x^3 + 40*x^2 + 125*x + 10, x^27 + 33*x^25 + 90*x^24 + 54*x^23 + 104*x^22 + 46*x^21 + 116*x^20 + 115*x^19 + 72*x^18 + 59*x^17 + 6*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 6*x^8 + 102*x^7 + 72*x^6 + 62*x^5 + 116*x^4 + 85*x^3 + 104*x^2 + 61*x + 90, x^27 + 33*x^25 + 34*x^24 + 54*x^23 + 56*x^22 + 78*x^21 + 84*x^20 + 51*x^19 + 120*x^18 + 91*x^17 + 46*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 30*x^8 + 102*x^7 + 88*x^6 + 94*x^5 + 20*x^4 + 21*x^3 + 88*x^2 + 93*x + 82, x^27 + 33*x^25 + 66*x^24 + 6*x^23 + 8*x^22 + 94*x^21 + 100*x^20 + 99*x^19 + 40*x^18 + 75*x^17 + 62*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 94*x^8 + 118*x^7 + 104*x^6 + 46*x^5 + 100*x^4 + 5*x^3 + 72*x^2 + 13*x + 98, x^27 + 33*x^25 + 98*x^24 + 6*x^23 + 104*x^22 + 94*x^21 + 4*x^20 + 99*x^19 + 72*x^18 + 75*x^17 + 62*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 126*x^8 + 118*x^7 + 72*x^6 + 46*x^5 + 4*x^4 + 5*x^3 + 104*x^2 + 13*x + 34, x^27 + 33*x^25 + 42*x^24 + 86*x^23 + 8*x^22 + 78*x^21 + 116*x^20 + 83*x^19 + 40*x^18 + 27*x^17 + 86*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 118*x^8 + 6*x^7 + 104*x^6 + 94*x^5 + 116*x^4 + 53*x^3 + 72*x^2 + 29*x + 74, x^27 + 33*x^25 + 42*x^24 + 118*x^23 + 72*x^22 + 110*x^21 + 52*x^20 + 51*x^19 + 104*x^18 + 123*x^17 + 22*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 118*x^8 + 38*x^7 + 40*x^6 + 126*x^5 + 52*x^4 + 21*x^3 + 8*x^2 + 125*x + 10, x^27 + 33*x^25 + 126*x^24 + 38*x^23 + 56*x^22 + 126*x^21 + 92*x^20 + 67*x^19 + 24*x^18 + 43*x^17 + 66*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 98*x^8 + 22*x^7 + 88*x^6 + 78*x^5 + 92*x^4 + 101*x^3 + 120*x^2 + 109*x + 30, x^27 + 33*x^25 + 54*x^24 + 6*x^23 + 40*x^22 + 62*x^21 + 124*x^20 + 35*x^19 + 40*x^18 + 43*x^17 + 26*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 74*x^8 + 118*x^7 + 8*x^6 + 14*x^5 + 60*x^4 + 69*x^3 + 72*x^2 + 109*x + 38, x^27 + 33*x^25 + 118*x^24 + 86*x^23 + 120*x^22 + 14*x^21 + 12*x^20 + 83*x^19 + 88*x^18 + 91*x^17 + 74*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 106*x^8 + 6*x^7 + 24*x^6 + 30*x^5 + 12*x^4 + 53*x^3 + 56*x^2 + 93*x + 22, x^27 + 33*x^25 + 102*x^24 + 70*x^23 + 72*x^22 + 62*x^21 + 124*x^20 + 99*x^19 + 8*x^18 + 43*x^17 + 74*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 90*x^8 + 54*x^7 + 40*x^6 + 14*x^5 + 60*x^4 + 5*x^3 + 40*x^2 + 109*x + 54, x^27 + 33*x^25 + 38*x^24 + 86*x^23 + 56*x^22 + 14*x^21 + 108*x^20 + 83*x^19 + 24*x^18 + 91*x^17 + 26*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 58*x^8 + 6*x^7 + 88*x^6 + 30*x^5 + 108*x^4 + 53*x^3 + 120*x^2 + 93*x + 70, x^27 + 33*x^25 + 110*x^24 + 118*x^23 + 104*x^22 + 78*x^21 + 108*x^20 + 115*x^19 + 104*x^18 + 91*x^17 + 34*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 18*x^8 + 38*x^7 + 72*x^6 + 94*x^5 + 44*x^4 + 85*x^3 + 8*x^2 + 93*x + 30, x^27 + 33*x^25 + 74*x^24 + 6*x^23 + 56*x^22 + 62*x^21 + 100*x^20 + 35*x^19 + 120*x^18 + 43*x^17 + 6*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 118*x^8 + 118*x^7 + 88*x^6 + 14*x^5 + 36*x^4 + 69*x^3 + 88*x^2 + 109*x + 122, x^27 + 33*x^25 + 42*x^24 + 102*x^23 + 24*x^22 + 30*x^21 + 4*x^20 + 67*x^19 + 24*x^18 + 75*x^17 + 70*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 86*x^8 + 86*x^7 + 56*x^6 + 110*x^5 + 68*x^4 + 101*x^3 + 120*x^2 + 13*x + 122, x^27 + 33*x^25 + 106*x^24 + 22*x^23 + 40*x^22 + 14*x^21 + 20*x^20 + 19*x^19 + 8*x^18 + 91*x^17 + 118*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 118*x^8 + 70*x^7 + 8*x^6 + 30*x^5 + 20*x^4 + 117*x^3 + 40*x^2 + 93*x + 106, x^27 + 33*x^25 + 6*x^24 + 70*x^23 + 104*x^22 + 62*x^21 + 92*x^20 + 99*x^19 + 104*x^18 + 43*x^17 + 10*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 122*x^8 + 54*x^7 + 72*x^6 + 14*x^5 + 28*x^4 + 5*x^3 + 8*x^2 + 109*x + 54, x^27 + 33*x^25 + 22*x^24 + 118*x^23 + 24*x^22 + 46*x^21 + 108*x^20 + 51*x^19 + 56*x^18 + 59*x^17 + 10*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 10*x^8 + 38*x^7 + 56*x^6 + 62*x^5 + 108*x^4 + 21*x^3 + 24*x^2 + 61*x + 22, x^27 + 33*x^25 + 38*x^24 + 6*x^23 + 72*x^22 + 62*x^21 + 60*x^20 + 35*x^19 + 8*x^18 + 43*x^17 + 74*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 26*x^8 + 118*x^7 + 40*x^6 + 14*x^5 + 124*x^4 + 69*x^3 + 40*x^2 + 109*x + 54, x^27 + 33*x^25 + 18*x^24 + 70*x^23 + 8*x^22 + 30*x^21 + 68*x^20 + 35*x^19 + 40*x^18 + 11*x^17 + 46*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 14*x^8 + 54*x^7 + 104*x^6 + 110*x^5 + 68*x^4 + 69*x^3 + 72*x^2 + 77*x + 114, x^27 + 33*x^25 + 14*x^24 + 102*x^23 + 88*x^22 + 62*x^21 + 92*x^20 + 3*x^19 + 120*x^18 + 107*x^17 + 82*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 18*x^8 + 86*x^7 + 120*x^6 + 14*x^5 + 92*x^4 + 37*x^3 + 88*x^2 + 45*x + 78, x^27 + 33*x^25 + 66*x^24 + 102*x^23 + 8*x^22 + 62*x^21 + 100*x^20 + 3*x^19 + 40*x^18 + 107*x^17 + 62*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 94*x^8 + 86*x^7 + 104*x^6 + 14*x^5 + 100*x^4 + 37*x^3 + 72*x^2 + 45*x + 98, x^27 + 33*x^25 + 30*x^24 + 118*x^23 + 40*x^22 + 14*x^21 + 12*x^20 + 115*x^19 + 40*x^18 + 27*x^17 + 50*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 98*x^8 + 38*x^7 + 8*x^6 + 30*x^5 + 76*x^4 + 85*x^3 + 72*x^2 + 29*x + 14, x^27 + 33*x^25 + 114*x^24 + 86*x^23 + 56*x^22 + 46*x^21 + 116*x^20 + 19*x^19 + 120*x^18 + 123*x^17 + 94*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 78*x^8 + 6*x^7 + 88*x^6 + 62*x^5 + 52*x^4 + 117*x^3 + 88*x^2 + 125*x + 34, x^27 + 33*x^25 + 94*x^24 + 6*x^23 + 120*x^22 + 30*x^21 + 28*x^20 + 99*x^19 + 88*x^18 + 11*x^17 + 98*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 2*x^8 + 118*x^7 + 24*x^6 + 110*x^5 + 28*x^4 + 5*x^3 + 56*x^2 + 77*x + 126, x^27 + 33*x^25 + 38*x^24 + 38*x^23 + 8*x^22 + 30*x^21 + 60*x^20 + 3*x^19 + 72*x^18 + 75*x^17 + 74*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 26*x^8 + 22*x^7 + 104*x^6 + 110*x^5 + 124*x^4 + 37*x^3 + 104*x^2 + 13*x + 54, x^27 + 33*x^25 + 22*x^24 + 86*x^23 + 120*x^22 + 14*x^21 + 76*x^20 + 83*x^19 + 88*x^18 + 91*x^17 + 42*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 74*x^8 + 6*x^7 + 24*x^6 + 30*x^5 + 76*x^4 + 53*x^3 + 56*x^2 + 93*x + 54, x^27 + 33*x^25 + 122*x^24 + 102*x^23 + 56*x^22 + 30*x^21 + 4*x^20 + 67*x^19 + 120*x^18 + 75*x^17 + 22*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 70*x^8 + 86*x^7 + 88*x^6 + 110*x^5 + 68*x^4 + 101*x^3 + 88*x^2 + 13*x + 106, x^27 + 33*x^25 + 74*x^24 + 6*x^23 + 56*x^22 + 126*x^21 + 36*x^20 + 35*x^19 + 120*x^18 + 107*x^17 + 70*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 118*x^8 + 118*x^7 + 88*x^6 + 78*x^5 + 100*x^4 + 69*x^3 + 88*x^2 + 45*x + 58, x^27 + 33*x^25 + 90*x^24 + 102*x^23 + 56*x^22 + 94*x^21 + 4*x^20 + 67*x^19 + 120*x^18 + 11*x^17 + 118*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 102*x^8 + 86*x^7 + 88*x^6 + 46*x^5 + 68*x^4 + 101*x^3 + 88*x^2 + 77*x + 10, x^27 + 33*x^25 + 106*x^24 + 118*x^23 + 40*x^22 + 110*x^21 + 20*x^20 + 51*x^19 + 8*x^18 + 123*x^17 + 118*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 118*x^8 + 38*x^7 + 8*x^6 + 126*x^5 + 20*x^4 + 21*x^3 + 40*x^2 + 125*x + 106, x^27 + 33*x^25 + 114*x^24 + 54*x^23 + 88*x^22 + 14*x^21 + 20*x^20 + 51*x^19 + 88*x^18 + 27*x^17 + 62*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 14*x^8 + 102*x^7 + 120*x^6 + 30*x^5 + 84*x^4 + 21*x^3 + 56*x^2 + 29*x + 2, x^27 + 33*x^25 + 22*x^24 + 86*x^23 + 120*x^22 + 78*x^21 + 12*x^20 + 83*x^19 + 88*x^18 + 27*x^17 + 106*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 74*x^8 + 6*x^7 + 24*x^6 + 94*x^5 + 12*x^4 + 53*x^3 + 56*x^2 + 29*x + 118, x^27 + 33*x^25 + 2*x^24 + 38*x^23 + 104*x^22 + 126*x^21 + 68*x^20 + 67*x^19 + 72*x^18 + 43*x^17 + 30*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 94*x^8 + 22*x^7 + 72*x^6 + 78*x^5 + 68*x^4 + 101*x^3 + 104*x^2 + 109*x + 66, x^27 + 33*x^25 + 78*x^24 + 86*x^23 + 72*x^22 + 46*x^21 + 12*x^20 + 19*x^19 + 8*x^18 + 123*x^17 + 98*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 114*x^8 + 6*x^7 + 40*x^6 + 62*x^5 + 76*x^4 + 117*x^3 + 40*x^2 + 125*x + 30, x^27 + 33*x^25 + 78*x^24 + 6*x^23 + 56*x^22 + 30*x^21 + 124*x^20 + 99*x^19 + 24*x^18 + 11*x^17 + 114*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 18*x^8 + 118*x^7 + 88*x^6 + 110*x^5 + 124*x^4 + 5*x^3 + 120*x^2 + 77*x + 110, x^27 + 33*x^25 + 30*x^24 + 38*x^23 + 56*x^22 + 126*x^21 + 28*x^20 + 67*x^19 + 24*x^18 + 43*x^17 + 34*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 66*x^8 + 22*x^7 + 88*x^6 + 78*x^5 + 28*x^4 + 101*x^3 + 120*x^2 + 109*x + 62, x^27 + 33*x^25 + 98*x^24 + 118*x^23 + 120*x^22 + 14*x^21 + 20*x^20 + 115*x^19 + 56*x^18 + 27*x^17 + 46*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 94*x^8 + 38*x^7 + 24*x^6 + 30*x^5 + 84*x^4 + 85*x^3 + 24*x^2 + 29*x + 82, x^27 + 33*x^25 + 46*x^24 + 70*x^23 + 56*x^22 + 30*x^21 + 124*x^20 + 35*x^19 + 24*x^18 + 11*x^17 + 82*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 50*x^8 + 54*x^7 + 88*x^6 + 110*x^5 + 124*x^4 + 69*x^3 + 120*x^2 + 77*x + 14, x^27 + 33*x^25 + 14*x^24 + 22*x^23 + 40*x^22 + 46*x^21 + 44*x^20 + 83*x^19 + 40*x^18 + 123*x^17 + 2*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 114*x^8 + 70*x^7 + 8*x^6 + 62*x^5 + 108*x^4 + 53*x^3 + 72*x^2 + 125*x + 62, x^27 + 33*x^25 + 30*x^24 + 102*x^23 + 56*x^22 + 62*x^21 + 28*x^20 + 3*x^19 + 24*x^18 + 107*x^17 + 34*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 66*x^8 + 86*x^7 + 88*x^6 + 14*x^5 + 28*x^4 + 37*x^3 + 120*x^2 + 45*x + 62, x^27 + 33*x^25 + 54*x^24 + 102*x^23 + 40*x^22 + 94*x^21 + 60*x^20 + 67*x^19 + 40*x^18 + 11*x^17 + 90*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 74*x^8 + 86*x^7 + 8*x^6 + 46*x^5 + 124*x^4 + 101*x^3 + 72*x^2 + 77*x + 102, x^27 + 33*x^25 + 74*x^24 + 22*x^23 + 8*x^22 + 78*x^21 + 116*x^20 + 19*x^19 + 40*x^18 + 27*x^17 + 118*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 86*x^8 + 70*x^7 + 104*x^6 + 94*x^5 + 116*x^4 + 117*x^3 + 72*x^2 + 29*x + 42, x^27 + 33*x^25 + 62*x^24 + 70*x^23 + 88*x^22 + 94*x^21 + 60*x^20 + 35*x^19 + 120*x^18 + 75*x^17 + 34*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 98*x^8 + 54*x^7 + 120*x^6 + 46*x^5 + 60*x^4 + 69*x^3 + 88*x^2 + 13*x + 126, x^27 + 33*x^25 + 126*x^24 + 70*x^23 + 88*x^22 + 94*x^21 + 60*x^20 + 35*x^19 + 120*x^18 + 75*x^17 + 98*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 34*x^8 + 54*x^7 + 120*x^6 + 46*x^5 + 60*x^4 + 69*x^3 + 88*x^2 + 13*x + 62, x^27 + 33*x^25 + 54*x^24 + 22*x^23 + 56*x^22 + 78*x^21 + 76*x^20 + 19*x^19 + 24*x^18 + 27*x^17 + 74*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 42*x^8 + 70*x^7 + 88*x^6 + 94*x^5 + 76*x^4 + 117*x^3 + 120*x^2 + 29*x + 22, x^27 + 33*x^25 + 82*x^24 + 102*x^23 + 72*x^22 + 62*x^21 + 4*x^20 + 3*x^19 + 104*x^18 + 107*x^17 + 46*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 78*x^8 + 86*x^7 + 40*x^6 + 14*x^5 + 4*x^4 + 37*x^3 + 8*x^2 + 45*x + 114, x^27 + 33*x^25 + 6*x^24 + 118*x^23 + 56*x^22 + 110*x^21 + 108*x^20 + 51*x^19 + 24*x^18 + 123*x^17 + 122*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 90*x^8 + 38*x^7 + 88*x^6 + 126*x^5 + 108*x^4 + 21*x^3 + 120*x^2 + 125*x + 102, x^27 + 33*x^25 + 110*x^24 + 22*x^23 + 40*x^22 + 110*x^21 + 44*x^20 + 83*x^19 + 40*x^18 + 59*x^17 + 98*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 18*x^8 + 70*x^7 + 8*x^6 + 126*x^5 + 108*x^4 + 53*x^3 + 72*x^2 + 61*x + 94, x^27 + 33*x^25 + 122*x^24 + 6*x^23 + 120*x^22 + 62*x^21 + 68*x^20 + 35*x^19 + 56*x^18 + 43*x^17 + 86*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 70*x^8 + 118*x^7 + 24*x^6 + 14*x^5 + 4*x^4 + 69*x^3 + 24*x^2 + 109*x + 42, x^27 + 33*x^25 + 78*x^24 + 102*x^23 + 24*x^22 + 62*x^21 + 28*x^20 + 3*x^19 + 56*x^18 + 107*x^17 + 82*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 82*x^8 + 86*x^7 + 56*x^6 + 14*x^5 + 28*x^4 + 37*x^3 + 24*x^2 + 45*x + 78, x^27 + 33*x^25 + 126*x^24 + 22*x^23 + 8*x^22 + 110*x^21 + 108*x^20 + 83*x^19 + 72*x^18 + 59*x^17 + 50*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 66*x^8 + 70*x^7 + 104*x^6 + 126*x^5 + 44*x^4 + 53*x^3 + 104*x^2 + 61*x + 78, x^27 + 33*x^25 + 118*x^24 + 22*x^23 + 120*x^22 + 78*x^21 + 12*x^20 + 19*x^19 + 88*x^18 + 27*x^17 + 74*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 106*x^8 + 70*x^7 + 24*x^6 + 94*x^5 + 12*x^4 + 117*x^3 + 56*x^2 + 29*x + 22, x^27 + 33*x^25 + 70*x^24 + 118*x^23 + 56*x^22 + 46*x^21 + 44*x^20 + 51*x^19 + 24*x^18 + 59*x^17 + 122*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 26*x^8 + 38*x^7 + 88*x^6 + 62*x^5 + 44*x^4 + 21*x^3 + 120*x^2 + 61*x + 102, x^27 + 33*x^25 + 50*x^24 + 22*x^23 + 56*x^22 + 46*x^21 + 52*x^20 + 83*x^19 + 120*x^18 + 123*x^17 + 94*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 14*x^8 + 70*x^7 + 88*x^6 + 62*x^5 + 116*x^4 + 53*x^3 + 88*x^2 + 125*x + 34, x^27 + 33*x^25 + 66*x^24 + 38*x^23 + 40*x^22 + 126*x^21 + 4*x^20 + 67*x^19 + 8*x^18 + 43*x^17 + 30*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 30*x^8 + 22*x^7 + 8*x^6 + 78*x^5 + 4*x^4 + 101*x^3 + 40*x^2 + 109*x + 66, x^27 + 33*x^25 + 42*x^24 + 102*x^23 + 120*x^22 + 94*x^21 + 36*x^20 + 67*x^19 + 56*x^18 + 11*x^17 + 38*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 22*x^8 + 86*x^7 + 24*x^6 + 46*x^5 + 100*x^4 + 101*x^3 + 24*x^2 + 77*x + 90, x^27 + 33*x^25 + 26*x^24 + 86*x^23 + 72*x^22 + 14*x^21 + 20*x^20 + 83*x^19 + 104*x^18 + 91*x^17 + 38*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 6*x^8 + 6*x^7 + 40*x^6 + 30*x^5 + 20*x^4 + 53*x^3 + 8*x^2 + 93*x + 122, x^27 + 33*x^25 + 30*x^24 + 102*x^23 + 88*x^22 + 126*x^21 + 124*x^20 + 3*x^19 + 120*x^18 + 43*x^17 + 66*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 2*x^8 + 86*x^7 + 120*x^6 + 78*x^5 + 124*x^4 + 37*x^3 + 88*x^2 + 109*x + 94, x^27 + 33*x^25 + 6*x^24 + 86*x^23 + 56*x^22 + 78*x^21 + 108*x^20 + 83*x^19 + 24*x^18 + 27*x^17 + 122*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 90*x^8 + 6*x^7 + 88*x^6 + 94*x^5 + 108*x^4 + 53*x^3 + 120*x^2 + 29*x + 102, x^27 + 33*x^25 + 78*x^24 + 70*x^23 + 56*x^22 + 94*x^21 + 124*x^20 + 35*x^19 + 24*x^18 + 75*x^17 + 114*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 18*x^8 + 54*x^7 + 88*x^6 + 46*x^5 + 124*x^4 + 69*x^3 + 120*x^2 + 13*x + 110, x^27 + 33*x^25 + 2*x^24 + 102*x^23 + 8*x^22 + 62*x^21 + 100*x^20 + 3*x^19 + 40*x^18 + 107*x^17 + 126*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 30*x^8 + 86*x^7 + 104*x^6 + 14*x^5 + 100*x^4 + 37*x^3 + 72*x^2 + 45*x + 34, x^27 + 33*x^25 + 78*x^24 + 118*x^23 + 8*x^22 + 78*x^21 + 76*x^20 + 115*x^19 + 72*x^18 + 91*x^17 + 34*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 114*x^8 + 38*x^7 + 104*x^6 + 94*x^5 + 12*x^4 + 85*x^3 + 104*x^2 + 93*x + 94, x^27 + 33*x^25 + 66*x^24 + 86*x^23 + 88*x^22 + 110*x^21 + 52*x^20 + 19*x^19 + 88*x^18 + 59*x^17 + 110*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 62*x^8 + 6*x^7 + 120*x^6 + 126*x^5 + 116*x^4 + 117*x^3 + 56*x^2 + 61*x + 82, x^27 + 33*x^25 + 14*x^24 + 118*x^23 + 8*x^22 + 14*x^21 + 12*x^20 + 115*x^19 + 72*x^18 + 27*x^17 + 34*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 50*x^8 + 38*x^7 + 104*x^6 + 30*x^5 + 76*x^4 + 85*x^3 + 104*x^2 + 29*x + 94, x^27 + 33*x^25 + 22*x^24 + 70*x^23 + 8*x^22 + 126*x^21 + 28*x^20 + 99*x^19 + 72*x^18 + 107*x^17 + 90*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 42*x^8 + 54*x^7 + 104*x^6 + 78*x^5 + 92*x^4 + 5*x^3 + 104*x^2 + 45*x + 38, x^27 + 33*x^25 + 94*x^24 + 22*x^23 + 72*x^22 + 46*x^21 + 44*x^20 + 83*x^19 + 8*x^18 + 123*x^17 + 82*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 98*x^8 + 70*x^7 + 40*x^6 + 62*x^5 + 108*x^4 + 53*x^3 + 40*x^2 + 125*x + 46, x^27 + 33*x^25 + 10*x^24 + 70*x^23 + 120*x^22 + 126*x^21 + 36*x^20 + 99*x^19 + 56*x^18 + 107*x^17 + 6*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 54*x^8 + 54*x^7 + 24*x^6 + 78*x^5 + 100*x^4 + 5*x^3 + 24*x^2 + 45*x + 122, x^27 + 33*x^25 + 66*x^24 + 118*x^23 + 56*x^22 + 14*x^21 + 20*x^20 + 115*x^19 + 120*x^18 + 27*x^17 + 14*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 126*x^8 + 38*x^7 + 88*x^6 + 30*x^5 + 84*x^4 + 85*x^3 + 88*x^2 + 29*x + 114, x^27 + 33*x^25 + 82*x^24 + 118*x^23 + 120*x^22 + 78*x^21 + 116*x^20 + 115*x^19 + 56*x^18 + 91*x^17 + 62*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 110*x^8 + 38*x^7 + 24*x^6 + 94*x^5 + 52*x^4 + 85*x^3 + 24*x^2 + 93*x + 66, x^27 + 33*x^25 + 58*x^24 + 118*x^23 + 104*x^22 + 110*x^21 + 52*x^20 + 51*x^19 + 72*x^18 + 123*x^17 + 38*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 38*x^8 + 38*x^7 + 72*x^6 + 126*x^5 + 52*x^4 + 21*x^3 + 104*x^2 + 125*x + 58, x^27 + 33*x^25 + 118*x^24 + 86*x^23 + 120*x^22 + 78*x^21 + 76*x^20 + 83*x^19 + 88*x^18 + 27*x^17 + 10*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 106*x^8 + 6*x^7 + 24*x^6 + 94*x^5 + 76*x^4 + 53*x^3 + 56*x^2 + 29*x + 86, x^27 + 33*x^25 + 46*x^24 + 102*x^23 + 88*x^22 + 126*x^21 + 92*x^20 + 3*x^19 + 120*x^18 + 43*x^17 + 114*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 114*x^8 + 86*x^7 + 120*x^6 + 78*x^5 + 92*x^4 + 37*x^3 + 88*x^2 + 109*x + 46, x^27 + 33*x^25 + 62*x^24 + 38*x^23 + 56*x^22 + 62*x^21 + 28*x^20 + 67*x^19 + 24*x^18 + 107*x^17 + 66*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 34*x^8 + 22*x^7 + 88*x^6 + 14*x^5 + 28*x^4 + 101*x^3 + 120*x^2 + 45*x + 30, x^27 + 33*x^25 + 82*x^24 + 22*x^23 + 120*x^22 + 46*x^21 + 52*x^20 + 83*x^19 + 56*x^18 + 123*x^17 + 126*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 110*x^8 + 70*x^7 + 24*x^6 + 62*x^5 + 116*x^4 + 53*x^3 + 24*x^2 + 125*x + 2, x^27 + 33*x^25 + 82*x^24 + 38*x^23 + 8*x^22 + 126*x^21 + 68*x^20 + 67*x^19 + 40*x^18 + 43*x^17 + 110*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 78*x^8 + 22*x^7 + 104*x^6 + 78*x^5 + 68*x^4 + 101*x^3 + 72*x^2 + 109*x + 50, x^27 + 33*x^25 + 22*x^24 + 38*x^23 + 72*x^22 + 30*x^21 + 28*x^20 + 3*x^19 + 8*x^18 + 75*x^17 + 90*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 42*x^8 + 22*x^7 + 40*x^6 + 110*x^5 + 92*x^4 + 37*x^3 + 40*x^2 + 13*x + 38, x^27 + 33*x^25 + 106*x^24 + 38*x^23 + 120*x^22 + 30*x^21 + 36*x^20 + 3*x^19 + 56*x^18 + 75*x^17 + 102*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 86*x^8 + 22*x^7 + 24*x^6 + 110*x^5 + 100*x^4 + 37*x^3 + 24*x^2 + 13*x + 26, x^27 + 33*x^25 + 30*x^24 + 70*x^23 + 120*x^22 + 94*x^21 + 28*x^20 + 35*x^19 + 88*x^18 + 75*x^17 + 34*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 66*x^8 + 54*x^7 + 24*x^6 + 46*x^5 + 28*x^4 + 69*x^3 + 56*x^2 + 13*x + 62, x^27 + 33*x^25 + 30*x^24 + 102*x^23 + 56*x^22 + 126*x^21 + 92*x^20 + 3*x^19 + 24*x^18 + 43*x^17 + 98*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 66*x^8 + 86*x^7 + 88*x^6 + 78*x^5 + 92*x^4 + 37*x^3 + 120*x^2 + 109*x + 126, x^27 + 33*x^25 + 126*x^24 + 54*x^23 + 8*x^22 + 14*x^21 + 108*x^20 + 51*x^19 + 72*x^18 + 27*x^17 + 50*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 66*x^8 + 102*x^7 + 104*x^6 + 30*x^5 + 44*x^4 + 21*x^3 + 104*x^2 + 29*x + 78, x^27 + 33*x^25 + 98*x^24 + 38*x^23 + 104*x^22 + 126*x^21 + 4*x^20 + 67*x^19 + 72*x^18 + 43*x^17 + 62*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 126*x^8 + 22*x^7 + 72*x^6 + 78*x^5 + 4*x^4 + 101*x^3 + 104*x^2 + 109*x + 34, x^27 + 33*x^25 + 66*x^24 + 38*x^23 + 104*x^22 + 62*x^21 + 4*x^20 + 67*x^19 + 72*x^18 + 107*x^17 + 30*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 30*x^8 + 22*x^7 + 72*x^6 + 14*x^5 + 4*x^4 + 101*x^3 + 104*x^2 + 45*x + 66, x^27 + 33*x^25 + 102*x^24 + 86*x^23 + 56*x^22 + 78*x^21 + 44*x^20 + 83*x^19 + 24*x^18 + 27*x^17 + 26*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 122*x^8 + 6*x^7 + 88*x^6 + 94*x^5 + 44*x^4 + 53*x^3 + 120*x^2 + 29*x + 70, x^27 + 33*x^25 + 70*x^24 + 6*x^23 + 40*x^22 + 62*x^21 + 92*x^20 + 35*x^19 + 40*x^18 + 43*x^17 + 74*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 58*x^8 + 118*x^7 + 8*x^6 + 14*x^5 + 28*x^4 + 69*x^3 + 72*x^2 + 109*x + 118, x^27 + 33*x^25 + 126*x^24 + 38*x^23 + 88*x^22 + 62*x^21 + 60*x^20 + 67*x^19 + 120*x^18 + 107*x^17 + 98*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 34*x^8 + 22*x^7 + 120*x^6 + 14*x^5 + 60*x^4 + 101*x^3 + 88*x^2 + 45*x + 62, x^27 + 33*x^25 + 90*x^24 + 22*x^23 + 104*x^22 + 78*x^21 + 52*x^20 + 19*x^19 + 72*x^18 + 27*x^17 + 70*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 6*x^8 + 70*x^7 + 72*x^6 + 94*x^5 + 52*x^4 + 117*x^3 + 104*x^2 + 29*x + 26, x^27 + 33*x^25 + 14*x^24 + 102*x^23 + 88*x^22 + 126*x^21 + 28*x^20 + 3*x^19 + 120*x^18 + 43*x^17 + 18*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 18*x^8 + 86*x^7 + 120*x^6 + 78*x^5 + 28*x^4 + 37*x^3 + 88*x^2 + 109*x + 14, x^27 + 33*x^25 + 10*x^24 + 38*x^23 + 24*x^22 + 94*x^21 + 68*x^20 + 3*x^19 + 24*x^18 + 11*x^17 + 102*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 118*x^8 + 22*x^7 + 56*x^6 + 46*x^5 + 4*x^4 + 37*x^3 + 120*x^2 + 77*x + 90, x^27 + 33*x^25 + 102*x^24 + 70*x^23 + 104*x^22 + 126*x^21 + 92*x^20 + 99*x^19 + 104*x^18 + 107*x^17 + 106*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 26*x^8 + 54*x^7 + 72*x^6 + 78*x^5 + 28*x^4 + 5*x^3 + 8*x^2 + 45*x + 86, x^27 + 33*x^25 + 62*x^24 + 6*x^23 + 88*x^22 + 94*x^21 + 124*x^20 + 99*x^19 + 120*x^18 + 75*x^17 + 98*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 98*x^8 + 118*x^7 + 120*x^6 + 46*x^5 + 124*x^4 + 5*x^3 + 88*x^2 + 13*x + 62, x^27 + 33*x^25 + 94*x^24 + 54*x^23 + 72*x^22 + 78*x^21 + 44*x^20 + 51*x^19 + 8*x^18 + 91*x^17 + 82*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 98*x^8 + 102*x^7 + 40*x^6 + 94*x^5 + 108*x^4 + 21*x^3 + 40*x^2 + 93*x + 46, x^27 + 33*x^25 + 70*x^24 + 38*x^23 + 8*x^22 + 94*x^21 + 60*x^20 + 3*x^19 + 72*x^18 + 11*x^17 + 106*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 122*x^8 + 22*x^7 + 104*x^6 + 46*x^5 + 124*x^4 + 37*x^3 + 104*x^2 + 77*x + 22, x^27 + 33*x^25 + 98*x^24 + 102*x^23 + 104*x^22 + 62*x^21 + 4*x^20 + 3*x^19 + 72*x^18 + 107*x^17 + 62*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 126*x^8 + 86*x^7 + 72*x^6 + 14*x^5 + 4*x^4 + 37*x^3 + 104*x^2 + 45*x + 34, x^27 + 33*x^25 + 78*x^24 + 86*x^23 + 8*x^22 + 46*x^21 + 76*x^20 + 19*x^19 + 72*x^18 + 123*x^17 + 34*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 114*x^8 + 6*x^7 + 104*x^6 + 62*x^5 + 12*x^4 + 117*x^3 + 104*x^2 + 125*x + 94, x^27 + 33*x^25 + 74*x^24 + 38*x^23 + 88*x^22 + 30*x^21 + 68*x^20 + 3*x^19 + 88*x^18 + 75*x^17 + 38*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 54*x^8 + 22*x^7 + 120*x^6 + 110*x^5 + 4*x^4 + 37*x^3 + 56*x^2 + 13*x + 26, x^27 + 33*x^25 + 50*x^24 + 70*x^23 + 8*x^22 + 94*x^21 + 68*x^20 + 35*x^19 + 40*x^18 + 75*x^17 + 78*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 110*x^8 + 54*x^7 + 104*x^6 + 46*x^5 + 68*x^4 + 69*x^3 + 72*x^2 + 13*x + 82, x^27 + 33*x^25 + 42*x^24 + 38*x^23 + 120*x^22 + 30*x^21 + 36*x^20 + 3*x^19 + 56*x^18 + 75*x^17 + 38*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 22*x^8 + 22*x^7 + 24*x^6 + 110*x^5 + 100*x^4 + 37*x^3 + 24*x^2 + 13*x + 90, x^27 + 33*x^25 + 66*x^24 + 22*x^23 + 88*x^22 + 110*x^21 + 116*x^20 + 83*x^19 + 88*x^18 + 59*x^17 + 46*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 62*x^8 + 70*x^7 + 120*x^6 + 126*x^5 + 52*x^4 + 53*x^3 + 56*x^2 + 61*x + 18, x^27 + 33*x^25 + 70*x^24 + 102*x^23 + 104*x^22 + 30*x^21 + 28*x^20 + 67*x^19 + 104*x^18 + 75*x^17 + 10*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 58*x^8 + 86*x^7 + 72*x^6 + 110*x^5 + 92*x^4 + 101*x^3 + 8*x^2 + 13*x + 54, x^27 + 33*x^25 + 90*x^24 + 38*x^23 + 24*x^22 + 94*x^21 + 36*x^20 + 3*x^19 + 24*x^18 + 11*x^17 + 86*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 38*x^8 + 22*x^7 + 56*x^6 + 46*x^5 + 100*x^4 + 37*x^3 + 120*x^2 + 77*x + 106, x^27 + 33*x^25 + 102*x^24 + 102*x^23 + 40*x^22 + 94*x^21 + 92*x^20 + 67*x^19 + 40*x^18 + 11*x^17 + 106*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 26*x^8 + 86*x^7 + 8*x^6 + 46*x^5 + 28*x^4 + 101*x^3 + 72*x^2 + 77*x + 86, x^27 + 33*x^25 + 98*x^24 + 6*x^23 + 40*x^22 + 94*x^21 + 68*x^20 + 99*x^19 + 8*x^18 + 75*x^17 + 126*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 126*x^8 + 118*x^7 + 8*x^6 + 46*x^5 + 68*x^4 + 5*x^3 + 40*x^2 + 13*x + 98, x^27 + 33*x^25 + 86*x^24 + 70*x^23 + 40*x^22 + 126*x^21 + 60*x^20 + 99*x^19 + 40*x^18 + 107*x^17 + 122*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 42*x^8 + 54*x^7 + 8*x^6 + 78*x^5 + 124*x^4 + 5*x^3 + 72*x^2 + 45*x + 70, x^27 + 33*x^25 + 2*x^24 + 70*x^23 + 104*x^22 + 94*x^21 + 4*x^20 + 35*x^19 + 72*x^18 + 75*x^17 + 94*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 94*x^8 + 54*x^7 + 72*x^6 + 46*x^5 + 4*x^4 + 69*x^3 + 104*x^2 + 13*x + 2, x^27 + 33*x^25 + 46*x^24 + 86*x^23 + 72*x^22 + 110*x^21 + 12*x^20 + 19*x^19 + 8*x^18 + 59*x^17 + 66*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 18*x^8 + 6*x^7 + 40*x^6 + 126*x^5 + 76*x^4 + 117*x^3 + 40*x^2 + 61*x + 62, x^27 + 33*x^25 + 62*x^24 + 118*x^23 + 104*x^22 + 14*x^21 + 12*x^20 + 115*x^19 + 104*x^18 + 27*x^17 + 82*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 66*x^8 + 38*x^7 + 72*x^6 + 30*x^5 + 76*x^4 + 85*x^3 + 8*x^2 + 29*x + 110, x^27 + 33*x^25 + 42*x^24 + 118*x^23 + 72*x^22 + 46*x^21 + 116*x^20 + 51*x^19 + 104*x^18 + 59*x^17 + 86*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 118*x^8 + 38*x^7 + 40*x^6 + 62*x^5 + 116*x^4 + 21*x^3 + 8*x^2 + 61*x + 74, x^27 + 33*x^25 + 54*x^24 + 118*x^23 + 24*x^22 + 110*x^21 + 108*x^20 + 51*x^19 + 56*x^18 + 123*x^17 + 42*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 106*x^8 + 38*x^7 + 56*x^6 + 126*x^5 + 108*x^4 + 21*x^3 + 24*x^2 + 125*x + 118, x^27 + 33*x^25 + 90*x^24 + 70*x^23 + 56*x^22 + 126*x^21 + 68*x^20 + 99*x^19 + 120*x^18 + 107*x^17 + 54*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 102*x^8 + 54*x^7 + 88*x^6 + 78*x^5 + 4*x^4 + 5*x^3 + 88*x^2 + 45*x + 74, x^27 + 33*x^25 + 22*x^24 + 54*x^23 + 120*x^22 + 110*x^21 + 76*x^20 + 115*x^19 + 88*x^18 + 123*x^17 + 42*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 74*x^8 + 102*x^7 + 24*x^6 + 126*x^5 + 76*x^4 + 85*x^3 + 56*x^2 + 125*x + 54, x^27 + 33*x^25 + 6*x^24 + 70*x^23 + 40*x^22 + 62*x^21 + 28*x^20 + 99*x^19 + 40*x^18 + 43*x^17 + 74*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 122*x^8 + 54*x^7 + 8*x^6 + 14*x^5 + 92*x^4 + 5*x^3 + 72*x^2 + 109*x + 118, x^27 + 33*x^25 + 126*x^24 + 118*x^23 + 104*x^22 + 78*x^21 + 76*x^20 + 115*x^19 + 104*x^18 + 91*x^17 + 82*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 2*x^8 + 38*x^7 + 72*x^6 + 94*x^5 + 12*x^4 + 85*x^3 + 8*x^2 + 93*x + 110, x^27 + 33*x^25 + 2*x^24 + 118*x^23 + 120*x^22 + 78*x^21 + 20*x^20 + 115*x^19 + 56*x^18 + 91*x^17 + 78*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 62*x^8 + 38*x^7 + 24*x^6 + 94*x^5 + 84*x^4 + 85*x^3 + 24*x^2 + 93*x + 50, x^27 + 33*x^25 + 26*x^24 + 6*x^23 + 56*x^22 + 126*x^21 + 4*x^20 + 35*x^19 + 120*x^18 + 107*x^17 + 54*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 38*x^8 + 118*x^7 + 88*x^6 + 78*x^5 + 68*x^4 + 69*x^3 + 88*x^2 + 45*x + 74, x^27 + 33*x^25 + 98*x^24 + 118*x^23 + 88*x^22 + 14*x^21 + 116*x^20 + 115*x^19 + 88*x^18 + 27*x^17 + 78*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 30*x^8 + 38*x^7 + 120*x^6 + 30*x^5 + 52*x^4 + 85*x^3 + 56*x^2 + 29*x + 114, x^27 + 33*x^25 + 102*x^24 + 54*x^23 + 88*x^22 + 110*x^21 + 12*x^20 + 115*x^19 + 120*x^18 + 123*x^17 + 58*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 58*x^8 + 102*x^7 + 120*x^6 + 126*x^5 + 12*x^4 + 85*x^3 + 88*x^2 + 125*x + 102, x^27 + 33*x^25 + 74*x^24 + 38*x^23 + 24*x^22 + 30*x^21 + 4*x^20 + 3*x^19 + 24*x^18 + 75*x^17 + 102*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 54*x^8 + 22*x^7 + 56*x^6 + 110*x^5 + 68*x^4 + 37*x^3 + 120*x^2 + 13*x + 90, x^27 + 33*x^25 + 30*x^24 + 70*x^23 + 56*x^22 + 30*x^21 + 28*x^20 + 35*x^19 + 24*x^18 + 11*x^17 + 34*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 66*x^8 + 54*x^7 + 88*x^6 + 110*x^5 + 28*x^4 + 69*x^3 + 120*x^2 + 77*x + 62, x^27 + 33*x^25 + 98*x^24 + 86*x^23 + 120*x^22 + 110*x^21 + 20*x^20 + 19*x^19 + 56*x^18 + 59*x^17 + 46*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 94*x^8 + 6*x^7 + 24*x^6 + 126*x^5 + 84*x^4 + 117*x^3 + 24*x^2 + 61*x + 82, x^27 + 33*x^25 + 90*x^24 + 86*x^23 + 40*x^22 + 14*x^21 + 116*x^20 + 83*x^19 + 8*x^18 + 91*x^17 + 6*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 6*x^8 + 6*x^7 + 8*x^6 + 30*x^5 + 116*x^4 + 53*x^3 + 40*x^2 + 93*x + 90, x^27 + 33*x^25 + 106*x^24 + 6*x^23 + 120*x^22 + 62*x^21 + 100*x^20 + 35*x^19 + 56*x^18 + 43*x^17 + 38*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 86*x^8 + 118*x^7 + 24*x^6 + 14*x^5 + 36*x^4 + 69*x^3 + 24*x^2 + 109*x + 90, x^27 + 33*x^25 + 114*x^24 + 102*x^23 + 104*x^22 + 126*x^21 + 36*x^20 + 3*x^19 + 72*x^18 + 43*x^17 + 46*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 110*x^8 + 86*x^7 + 72*x^6 + 78*x^5 + 36*x^4 + 37*x^3 + 104*x^2 + 109*x + 50, x^27 + 33*x^25 + 22*x^24 + 6*x^23 + 8*x^22 + 126*x^21 + 92*x^20 + 35*x^19 + 72*x^18 + 107*x^17 + 26*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 42*x^8 + 118*x^7 + 104*x^6 + 78*x^5 + 28*x^4 + 69*x^3 + 104*x^2 + 45*x + 102, x^27 + 33*x^25 + 126*x^24 + 70*x^23 + 120*x^22 + 94*x^21 + 92*x^20 + 35*x^19 + 88*x^18 + 75*x^17 + 66*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 98*x^8 + 54*x^7 + 24*x^6 + 46*x^5 + 92*x^4 + 69*x^3 + 56*x^2 + 13*x + 30, x^27 + 33*x^25 + 78*x^24 + 70*x^23 + 88*x^22 + 94*x^21 + 28*x^20 + 35*x^19 + 120*x^18 + 75*x^17 + 82*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 82*x^8 + 54*x^7 + 120*x^6 + 46*x^5 + 28*x^4 + 69*x^3 + 88*x^2 + 13*x + 78, x^27 + 33*x^25 + 38*x^24 + 118*x^23 + 88*x^22 + 46*x^21 + 12*x^20 + 51*x^19 + 120*x^18 + 59*x^17 + 122*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 122*x^8 + 38*x^7 + 120*x^6 + 62*x^5 + 12*x^4 + 21*x^3 + 88*x^2 + 61*x + 38, x^27 + 33*x^25 + 66*x^24 + 102*x^23 + 40*x^22 + 62*x^21 + 4*x^20 + 3*x^19 + 8*x^18 + 107*x^17 + 30*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 30*x^8 + 86*x^7 + 8*x^6 + 14*x^5 + 4*x^4 + 37*x^3 + 40*x^2 + 45*x + 66, x^27 + 33*x^25 + 50*x^24 + 118*x^23 + 88*x^22 + 14*x^21 + 84*x^20 + 115*x^19 + 88*x^18 + 27*x^17 + 62*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 78*x^8 + 38*x^7 + 120*x^6 + 30*x^5 + 20*x^4 + 85*x^3 + 56*x^2 + 29*x + 2, x^27 + 33*x^25 + 102*x^24 + 22*x^23 + 56*x^22 + 14*x^21 + 44*x^20 + 19*x^19 + 24*x^18 + 91*x^17 + 26*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 122*x^8 + 70*x^7 + 88*x^6 + 30*x^5 + 44*x^4 + 117*x^3 + 120*x^2 + 93*x + 70, x^27 + 33*x^25 + 10*x^24 + 38*x^23 + 56*x^22 + 30*x^21 + 36*x^20 + 3*x^19 + 120*x^18 + 75*x^17 + 6*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 54*x^8 + 22*x^7 + 88*x^6 + 110*x^5 + 100*x^4 + 37*x^3 + 88*x^2 + 13*x + 122, x^27 + 33*x^25 + 18*x^24 + 86*x^23 + 24*x^22 + 46*x^21 + 20*x^20 + 19*x^19 + 24*x^18 + 123*x^17 + 94*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 110*x^8 + 6*x^7 + 56*x^6 + 62*x^5 + 84*x^4 + 117*x^3 + 120*x^2 + 125*x + 98, x^27 + 33*x^25 + 110*x^24 + 38*x^23 + 56*x^22 + 126*x^21 + 124*x^20 + 67*x^19 + 24*x^18 + 43*x^17 + 18*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 114*x^8 + 22*x^7 + 88*x^6 + 78*x^5 + 124*x^4 + 101*x^3 + 120*x^2 + 109*x + 78, x^27 + 33*x^25 + 38*x^24 + 102*x^23 + 40*x^22 + 30*x^21 + 28*x^20 + 67*x^19 + 40*x^18 + 75*x^17 + 106*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 90*x^8 + 86*x^7 + 8*x^6 + 110*x^5 + 92*x^4 + 101*x^3 + 72*x^2 + 13*x + 86, x^27 + 33*x^25 + 66*x^24 + 118*x^23 + 24*x^22 + 14*x^21 + 116*x^20 + 115*x^19 + 24*x^18 + 27*x^17 + 46*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 62*x^8 + 38*x^7 + 56*x^6 + 30*x^5 + 52*x^4 + 85*x^3 + 120*x^2 + 29*x + 18, x^27 + 33*x^25 + 98*x^24 + 118*x^23 + 88*x^22 + 78*x^21 + 52*x^20 + 115*x^19 + 88*x^18 + 91*x^17 + 14*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 30*x^8 + 38*x^7 + 120*x^6 + 94*x^5 + 116*x^4 + 85*x^3 + 56*x^2 + 93*x + 50, x^27 + 33*x^25 + 46*x^24 + 38*x^23 + 24*x^22 + 62*x^21 + 28*x^20 + 67*x^19 + 56*x^18 + 107*x^17 + 50*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 114*x^8 + 22*x^7 + 56*x^6 + 14*x^5 + 28*x^4 + 101*x^3 + 24*x^2 + 45*x + 110, x^27 + 33*x^25 + 98*x^24 + 70*x^23 + 72*x^22 + 30*x^21 + 100*x^20 + 35*x^19 + 104*x^18 + 11*x^17 + 94*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 62*x^8 + 54*x^7 + 40*x^6 + 110*x^5 + 100*x^4 + 69*x^3 + 8*x^2 + 77*x + 66, x^27 + 33*x^25 + 118*x^24 + 118*x^23 + 88*x^22 + 110*x^21 + 44*x^20 + 51*x^19 + 120*x^18 + 123*x^17 + 42*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 42*x^8 + 38*x^7 + 120*x^6 + 126*x^5 + 44*x^4 + 21*x^3 + 88*x^2 + 125*x + 118, x^27 + 33*x^25 + 82*x^24 + 54*x^23 + 88*x^22 + 78*x^21 + 20*x^20 + 51*x^19 + 88*x^18 + 91*x^17 + 30*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 46*x^8 + 102*x^7 + 120*x^6 + 94*x^5 + 84*x^4 + 21*x^3 + 56*x^2 + 93*x + 34, x^27 + 33*x^25 + 50*x^24 + 22*x^23 + 88*x^22 + 46*x^21 + 84*x^20 + 83*x^19 + 88*x^18 + 123*x^17 + 62*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 78*x^8 + 70*x^7 + 120*x^6 + 62*x^5 + 20*x^4 + 53*x^3 + 56*x^2 + 125*x + 2, x^27 + 33*x^25 + 114*x^24 + 6*x^23 + 40*x^22 + 30*x^21 + 100*x^20 + 99*x^19 + 8*x^18 + 11*x^17 + 110*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 110*x^8 + 118*x^7 + 8*x^6 + 110*x^5 + 100*x^4 + 5*x^3 + 40*x^2 + 77*x + 114, x^27 + 33*x^25 + 102*x^24 + 54*x^23 + 56*x^22 + 110*x^21 + 108*x^20 + 115*x^19 + 24*x^18 + 123*x^17 + 90*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 122*x^8 + 102*x^7 + 88*x^6 + 126*x^5 + 108*x^4 + 85*x^3 + 120*x^2 + 125*x + 6, x^27 + 33*x^25 + 46*x^24 + 102*x^23 + 24*x^22 + 126*x^21 + 28*x^20 + 3*x^19 + 56*x^18 + 43*x^17 + 50*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 114*x^8 + 86*x^7 + 56*x^6 + 78*x^5 + 28*x^4 + 37*x^3 + 24*x^2 + 109*x + 110, x^27 + 33*x^25 + 54*x^24 + 6*x^23 + 72*x^22 + 126*x^21 + 92*x^20 + 35*x^19 + 8*x^18 + 107*x^17 + 58*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 10*x^8 + 118*x^7 + 40*x^6 + 78*x^5 + 28*x^4 + 69*x^3 + 40*x^2 + 45*x + 70, x^27 + 33*x^25 + 10*x^24 + 70*x^23 + 24*x^22 + 126*x^21 + 68*x^20 + 99*x^19 + 24*x^18 + 107*x^17 + 102*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 118*x^8 + 54*x^7 + 56*x^6 + 78*x^5 + 4*x^4 + 5*x^3 + 120*x^2 + 45*x + 90, x^27 + 33*x^25 + 26*x^24 + 54*x^23 + 8*x^22 + 110*x^21 + 84*x^20 + 115*x^19 + 40*x^18 + 123*x^17 + 102*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 6*x^8 + 102*x^7 + 104*x^6 + 126*x^5 + 84*x^4 + 85*x^3 + 72*x^2 + 125*x + 58, x^27 + 33*x^25 + 94*x^24 + 102*x^23 + 56*x^22 + 62*x^21 + 28*x^20 + 3*x^19 + 24*x^18 + 107*x^17 + 98*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 2*x^8 + 86*x^7 + 88*x^6 + 14*x^5 + 28*x^4 + 37*x^3 + 120*x^2 + 45*x + 126, x^27 + 33*x^25 + 14*x^24 + 118*x^23 + 104*x^22 + 78*x^21 + 44*x^20 + 115*x^19 + 104*x^18 + 91*x^17 + 2*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 114*x^8 + 38*x^7 + 72*x^6 + 94*x^5 + 108*x^4 + 85*x^3 + 8*x^2 + 93*x + 62, x^27 + 33*x^25 + 98*x^24 + 54*x^23 + 88*x^22 + 78*x^21 + 116*x^20 + 51*x^19 + 88*x^18 + 91*x^17 + 78*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 30*x^8 + 102*x^7 + 120*x^6 + 94*x^5 + 52*x^4 + 21*x^3 + 56*x^2 + 93*x + 114, x^27 + 33*x^25 + 102*x^24 + 6*x^23 + 40*x^22 + 62*x^21 + 28*x^20 + 35*x^19 + 40*x^18 + 43*x^17 + 42*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 26*x^8 + 118*x^7 + 8*x^6 + 14*x^5 + 92*x^4 + 69*x^3 + 72*x^2 + 109*x + 22, x^27 + 33*x^25 + 78*x^24 + 70*x^23 + 120*x^22 + 30*x^21 + 124*x^20 + 35*x^19 + 88*x^18 + 11*x^17 + 114*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 18*x^8 + 54*x^7 + 24*x^6 + 110*x^5 + 124*x^4 + 69*x^3 + 56*x^2 + 77*x + 110, x^27 + 33*x^25 + 54*x^24 + 38*x^23 + 8*x^22 + 30*x^21 + 28*x^20 + 3*x^19 + 72*x^18 + 75*x^17 + 122*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 10*x^8 + 22*x^7 + 104*x^6 + 110*x^5 + 92*x^4 + 37*x^3 + 104*x^2 + 13*x + 6, x^27 + 33*x^25 + 98*x^24 + 70*x^23 + 8*x^22 + 94*x^21 + 100*x^20 + 35*x^19 + 40*x^18 + 75*x^17 + 94*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 62*x^8 + 54*x^7 + 104*x^6 + 46*x^5 + 100*x^4 + 69*x^3 + 72*x^2 + 13*x + 66, x^27 + 33*x^25 + 62*x^24 + 102*x^23 + 88*x^22 + 62*x^21 + 124*x^20 + 3*x^19 + 120*x^18 + 107*x^17 + 98*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 98*x^8 + 86*x^7 + 120*x^6 + 14*x^5 + 124*x^4 + 37*x^3 + 88*x^2 + 45*x + 62, x^27 + 33*x^25 + 114*x^24 + 70*x^23 + 8*x^22 + 94*x^21 + 68*x^20 + 35*x^19 + 40*x^18 + 75*x^17 + 14*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 46*x^8 + 54*x^7 + 104*x^6 + 46*x^5 + 68*x^4 + 69*x^3 + 72*x^2 + 13*x + 18, x^27 + 33*x^25 + 14*x^24 + 6*x^23 + 88*x^22 + 30*x^21 + 28*x^20 + 99*x^19 + 120*x^18 + 11*x^17 + 18*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 18*x^8 + 118*x^7 + 120*x^6 + 110*x^5 + 28*x^4 + 5*x^3 + 88*x^2 + 77*x + 14, x^27 + 33*x^25 + 82*x^24 + 70*x^23 + 104*x^22 + 30*x^21 + 36*x^20 + 35*x^19 + 72*x^18 + 11*x^17 + 14*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 14*x^8 + 54*x^7 + 72*x^6 + 110*x^5 + 36*x^4 + 69*x^3 + 104*x^2 + 77*x + 82, x^27 + 33*x^25 + 14*x^24 + 118*x^23 + 40*x^22 + 78*x^21 + 108*x^20 + 115*x^19 + 40*x^18 + 91*x^17 + 66*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 114*x^8 + 38*x^7 + 8*x^6 + 94*x^5 + 44*x^4 + 85*x^3 + 72*x^2 + 93*x + 126, x^27 + 33*x^25 + 58*x^24 + 102*x^23 + 88*x^22 + 30*x^21 + 36*x^20 + 67*x^19 + 88*x^18 + 75*x^17 + 54*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 70*x^8 + 86*x^7 + 120*x^6 + 110*x^5 + 100*x^4 + 101*x^3 + 56*x^2 + 13*x + 10, x^27 + 33*x^25 + 26*x^24 + 118*x^23 + 72*x^22 + 110*x^21 + 84*x^20 + 51*x^19 + 104*x^18 + 123*x^17 + 102*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 6*x^8 + 38*x^7 + 40*x^6 + 126*x^5 + 84*x^4 + 21*x^3 + 8*x^2 + 125*x + 58, x^27 + 33*x^25 + 26*x^24 + 38*x^23 + 120*x^22 + 30*x^21 + 68*x^20 + 3*x^19 + 56*x^18 + 75*x^17 + 118*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 38*x^8 + 22*x^7 + 24*x^6 + 110*x^5 + 4*x^4 + 37*x^3 + 24*x^2 + 13*x + 10, x^27 + 33*x^25 + 102*x^24 + 38*x^23 + 104*x^22 + 30*x^21 + 28*x^20 + 3*x^19 + 104*x^18 + 75*x^17 + 42*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 26*x^8 + 22*x^7 + 72*x^6 + 110*x^5 + 92*x^4 + 37*x^3 + 8*x^2 + 13*x + 22, x^27 + 33*x^25 + 126*x^24 + 86*x^23 + 104*x^22 + 110*x^21 + 12*x^20 + 19*x^19 + 104*x^18 + 59*x^17 + 18*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 2*x^8 + 6*x^7 + 72*x^6 + 126*x^5 + 76*x^4 + 117*x^3 + 8*x^2 + 61*x + 46, x^27 + 33*x^25 + 18*x^24 + 54*x^23 + 88*x^22 + 78*x^21 + 20*x^20 + 51*x^19 + 88*x^18 + 91*x^17 + 94*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 110*x^8 + 102*x^7 + 120*x^6 + 94*x^5 + 84*x^4 + 21*x^3 + 56*x^2 + 93*x + 98, x^27 + 33*x^25 + 118*x^24 + 54*x^23 + 24*x^22 + 110*x^21 + 44*x^20 + 115*x^19 + 56*x^18 + 123*x^17 + 42*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 42*x^8 + 102*x^7 + 56*x^6 + 126*x^5 + 44*x^4 + 85*x^3 + 24*x^2 + 125*x + 118, x^27 + 33*x^25 + 54*x^24 + 54*x^23 + 24*x^22 + 110*x^21 + 44*x^20 + 115*x^19 + 56*x^18 + 123*x^17 + 106*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 106*x^8 + 102*x^7 + 56*x^6 + 126*x^5 + 44*x^4 + 85*x^3 + 24*x^2 + 125*x + 54, x^27 + 33*x^25 + 82*x^24 + 22*x^23 + 120*x^22 + 110*x^21 + 116*x^20 + 83*x^19 + 56*x^18 + 59*x^17 + 62*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 110*x^8 + 70*x^7 + 24*x^6 + 126*x^5 + 52*x^4 + 53*x^3 + 24*x^2 + 61*x + 66, x^27 + 33*x^25 + 94*x^24 + 54*x^23 + 8*x^22 + 14*x^21 + 44*x^20 + 51*x^19 + 72*x^18 + 27*x^17 + 82*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 98*x^8 + 102*x^7 + 104*x^6 + 30*x^5 + 108*x^4 + 21*x^3 + 104*x^2 + 29*x + 46, x^27 + 33*x^25 + 58*x^24 + 102*x^23 + 24*x^22 + 94*x^21 + 36*x^20 + 67*x^19 + 24*x^18 + 11*x^17 + 54*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 70*x^8 + 86*x^7 + 56*x^6 + 46*x^5 + 100*x^4 + 101*x^3 + 120*x^2 + 77*x + 10, x^27 + 33*x^25 + 94*x^24 + 70*x^23 + 120*x^22 + 94*x^21 + 28*x^20 + 35*x^19 + 88*x^18 + 75*x^17 + 98*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 2*x^8 + 54*x^7 + 24*x^6 + 46*x^5 + 28*x^4 + 69*x^3 + 56*x^2 + 13*x + 126, x^27 + 33*x^25 + 118*x^24 + 118*x^23 + 56*x^22 + 110*x^21 + 12*x^20 + 51*x^19 + 24*x^18 + 123*x^17 + 74*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 106*x^8 + 38*x^7 + 88*x^6 + 126*x^5 + 12*x^4 + 21*x^3 + 120*x^2 + 125*x + 22, x^27 + 33*x^25 + 18*x^24 + 102*x^23 + 8*x^22 + 126*x^21 + 4*x^20 + 3*x^19 + 40*x^18 + 43*x^17 + 110*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 14*x^8 + 86*x^7 + 104*x^6 + 78*x^5 + 4*x^4 + 37*x^3 + 72*x^2 + 109*x + 50, x^27 + 33*x^25 + 86*x^24 + 6*x^23 + 104*x^22 + 62*x^21 + 124*x^20 + 35*x^19 + 104*x^18 + 43*x^17 + 58*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 42*x^8 + 118*x^7 + 72*x^6 + 14*x^5 + 60*x^4 + 69*x^3 + 8*x^2 + 109*x + 6, x^27 + 33*x^25 + 50*x^24 + 54*x^23 + 88*x^22 + 78*x^21 + 84*x^20 + 51*x^19 + 88*x^18 + 91*x^17 + 62*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 78*x^8 + 102*x^7 + 120*x^6 + 94*x^5 + 20*x^4 + 21*x^3 + 56*x^2 + 93*x + 2, x^27 + 33*x^25 + 98*x^24 + 38*x^23 + 40*x^22 + 126*x^21 + 68*x^20 + 67*x^19 + 8*x^18 + 43*x^17 + 126*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 126*x^8 + 22*x^7 + 8*x^6 + 78*x^5 + 68*x^4 + 101*x^3 + 40*x^2 + 109*x + 98, x^27 + 33*x^25 + 122*x^24 + 22*x^23 + 72*x^22 + 14*x^21 + 20*x^20 + 19*x^19 + 104*x^18 + 91*x^17 + 6*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 38*x^8 + 70*x^7 + 40*x^6 + 30*x^5 + 20*x^4 + 117*x^3 + 8*x^2 + 93*x + 26, x^27 + 33*x^25 + 102*x^24 + 54*x^23 + 88*x^22 + 46*x^21 + 76*x^20 + 115*x^19 + 120*x^18 + 59*x^17 + 122*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 58*x^8 + 102*x^7 + 120*x^6 + 62*x^5 + 76*x^4 + 85*x^3 + 88*x^2 + 61*x + 38, x^27 + 33*x^25 + 14*x^24 + 118*x^23 + 8*x^22 + 78*x^21 + 76*x^20 + 115*x^19 + 72*x^18 + 91*x^17 + 98*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 50*x^8 + 38*x^7 + 104*x^6 + 94*x^5 + 12*x^4 + 85*x^3 + 104*x^2 + 93*x + 30, x^27 + 33*x^25 + 86*x^24 + 22*x^23 + 56*x^22 + 14*x^21 + 76*x^20 + 19*x^19 + 24*x^18 + 91*x^17 + 106*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 10*x^8 + 70*x^7 + 88*x^6 + 30*x^5 + 76*x^4 + 117*x^3 + 120*x^2 + 93*x + 118, x^27 + 33*x^25 + 90*x^24 + 70*x^23 + 56*x^22 + 62*x^21 + 4*x^20 + 99*x^19 + 120*x^18 + 43*x^17 + 118*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 102*x^8 + 54*x^7 + 88*x^6 + 14*x^5 + 68*x^4 + 5*x^3 + 88*x^2 + 109*x + 10, x^27 + 33*x^25 + 98*x^24 + 86*x^23 + 88*x^22 + 46*x^21 + 52*x^20 + 19*x^19 + 88*x^18 + 123*x^17 + 14*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 30*x^8 + 6*x^7 + 120*x^6 + 62*x^5 + 116*x^4 + 117*x^3 + 56*x^2 + 125*x + 50, x^27 + 33*x^25 + 26*x^24 + 22*x^23 + 40*x^22 + 78*x^21 + 116*x^20 + 19*x^19 + 8*x^18 + 27*x^17 + 70*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 70*x^8 + 70*x^7 + 8*x^6 + 94*x^5 + 116*x^4 + 117*x^3 + 40*x^2 + 29*x + 26, x^27 + 33*x^25 + 34*x^24 + 70*x^23 + 8*x^22 + 30*x^21 + 36*x^20 + 35*x^19 + 40*x^18 + 11*x^17 + 94*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 126*x^8 + 54*x^7 + 104*x^6 + 110*x^5 + 36*x^4 + 69*x^3 + 72*x^2 + 77*x + 66, x^27 + 33*x^25 + 102*x^24 + 70*x^23 + 8*x^22 + 126*x^21 + 124*x^20 + 99*x^19 + 72*x^18 + 107*x^17 + 74*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 90*x^8 + 54*x^7 + 104*x^6 + 78*x^5 + 60*x^4 + 5*x^3 + 104*x^2 + 45*x + 54, x^27 + 33*x^25 + 82*x^24 + 86*x^23 + 88*x^22 + 110*x^21 + 20*x^20 + 19*x^19 + 88*x^18 + 59*x^17 + 30*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 46*x^8 + 6*x^7 + 120*x^6 + 126*x^5 + 84*x^4 + 117*x^3 + 56*x^2 + 61*x + 34, x^27 + 33*x^25 + 122*x^24 + 22*x^23 + 104*x^22 + 14*x^21 + 52*x^20 + 19*x^19 + 72*x^18 + 91*x^17 + 102*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 102*x^8 + 70*x^7 + 72*x^6 + 30*x^5 + 52*x^4 + 117*x^3 + 104*x^2 + 93*x + 122, x^27 + 33*x^25 + 122*x^24 + 70*x^23 + 120*x^22 + 62*x^21 + 4*x^20 + 99*x^19 + 56*x^18 + 43*x^17 + 22*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 70*x^8 + 54*x^7 + 24*x^6 + 14*x^5 + 68*x^4 + 5*x^3 + 24*x^2 + 109*x + 106, x^27 + 33*x^25 + 30*x^24 + 86*x^23 + 40*x^22 + 110*x^21 + 12*x^20 + 19*x^19 + 40*x^18 + 59*x^17 + 50*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 98*x^8 + 6*x^7 + 8*x^6 + 126*x^5 + 76*x^4 + 117*x^3 + 72*x^2 + 61*x + 14, x^27 + 33*x^25 + 26*x^24 + 6*x^23 + 56*x^22 + 62*x^21 + 68*x^20 + 35*x^19 + 120*x^18 + 43*x^17 + 118*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 38*x^8 + 118*x^7 + 88*x^6 + 14*x^5 + 4*x^4 + 69*x^3 + 88*x^2 + 109*x + 10, x^27 + 33*x^25 + 126*x^24 + 6*x^23 + 88*x^22 + 94*x^21 + 124*x^20 + 99*x^19 + 120*x^18 + 75*x^17 + 34*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 34*x^8 + 118*x^7 + 120*x^6 + 46*x^5 + 124*x^4 + 5*x^3 + 88*x^2 + 13*x + 126, x^27 + 33*x^25 + 18*x^24 + 118*x^23 + 56*x^22 + 14*x^21 + 116*x^20 + 115*x^19 + 120*x^18 + 27*x^17 + 126*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 46*x^8 + 38*x^7 + 88*x^6 + 30*x^5 + 52*x^4 + 85*x^3 + 88*x^2 + 29*x + 2, x^27 + 33*x^25 + 38*x^24 + 22*x^23 + 56*x^22 + 78*x^21 + 108*x^20 + 19*x^19 + 24*x^18 + 27*x^17 + 26*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 58*x^8 + 70*x^7 + 88*x^6 + 94*x^5 + 108*x^4 + 117*x^3 + 120*x^2 + 29*x + 70, x^27 + 33*x^25 + 90*x^24 + 54*x^23 + 72*x^22 + 110*x^21 + 20*x^20 + 115*x^19 + 104*x^18 + 123*x^17 + 102*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 70*x^8 + 102*x^7 + 40*x^6 + 126*x^5 + 20*x^4 + 85*x^3 + 8*x^2 + 125*x + 58, x^27 + 33*x^25 + 86*x^24 + 22*x^23 + 120*x^22 + 78*x^21 + 76*x^20 + 19*x^19 + 88*x^18 + 27*x^17 + 106*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 10*x^8 + 70*x^7 + 24*x^6 + 94*x^5 + 76*x^4 + 117*x^3 + 56*x^2 + 29*x + 118, x^27 + 33*x^25 + 54*x^24 + 22*x^23 + 24*x^22 + 78*x^21 + 44*x^20 + 19*x^19 + 56*x^18 + 27*x^17 + 106*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 106*x^8 + 70*x^7 + 56*x^6 + 94*x^5 + 44*x^4 + 117*x^3 + 24*x^2 + 29*x + 54, x^27 + 33*x^25 + 90*x^24 + 86*x^23 + 40*x^22 + 78*x^21 + 52*x^20 + 83*x^19 + 8*x^18 + 27*x^17 + 70*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 6*x^8 + 6*x^7 + 8*x^6 + 94*x^5 + 52*x^4 + 53*x^3 + 40*x^2 + 29*x + 26, x^27 + 33*x^25 + 106*x^24 + 22*x^23 + 40*x^22 + 78*x^21 + 84*x^20 + 19*x^19 + 8*x^18 + 27*x^17 + 54*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 118*x^8 + 70*x^7 + 8*x^6 + 94*x^5 + 84*x^4 + 117*x^3 + 40*x^2 + 29*x + 42, x^27 + 33*x^25 + 58*x^24 + 102*x^23 + 56*x^22 + 30*x^21 + 4*x^20 + 67*x^19 + 120*x^18 + 75*x^17 + 86*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 6*x^8 + 86*x^7 + 88*x^6 + 110*x^5 + 68*x^4 + 101*x^3 + 88*x^2 + 13*x + 42, x^27 + 33*x^25 + 6*x^24 + 102*x^23 + 72*x^22 + 94*x^21 + 60*x^20 + 67*x^19 + 8*x^18 + 11*x^17 + 42*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 58*x^8 + 86*x^7 + 40*x^6 + 46*x^5 + 124*x^4 + 101*x^3 + 40*x^2 + 77*x + 86, x^27 + 33*x^25 + 82*x^24 + 70*x^23 + 40*x^22 + 30*x^21 + 100*x^20 + 35*x^19 + 8*x^18 + 11*x^17 + 78*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 14*x^8 + 54*x^7 + 8*x^6 + 110*x^5 + 100*x^4 + 69*x^3 + 40*x^2 + 77*x + 18, x^27 + 33*x^25 + 106*x^24 + 54*x^23 + 72*x^22 + 110*x^21 + 116*x^20 + 115*x^19 + 104*x^18 + 123*x^17 + 22*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 54*x^8 + 102*x^7 + 40*x^6 + 126*x^5 + 116*x^4 + 85*x^3 + 8*x^2 + 125*x + 10, x^27 + 33*x^25 + 94*x^24 + 86*x^23 + 8*x^22 + 46*x^21 + 44*x^20 + 19*x^19 + 72*x^18 + 123*x^17 + 82*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 98*x^8 + 6*x^7 + 104*x^6 + 62*x^5 + 108*x^4 + 117*x^3 + 104*x^2 + 125*x + 46, x^27 + 33*x^25 + 118*x^24 + 6*x^23 + 104*x^22 + 62*x^21 + 60*x^20 + 35*x^19 + 104*x^18 + 43*x^17 + 26*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 10*x^8 + 118*x^7 + 72*x^6 + 14*x^5 + 124*x^4 + 69*x^3 + 8*x^2 + 109*x + 38, x^27 + 33*x^25 + 6*x^24 + 70*x^23 + 8*x^22 + 62*x^21 + 124*x^20 + 99*x^19 + 72*x^18 + 43*x^17 + 106*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 58*x^8 + 54*x^7 + 104*x^6 + 14*x^5 + 60*x^4 + 5*x^3 + 104*x^2 + 109*x + 22, x^27 + 33*x^25 + 74*x^24 + 22*x^23 + 72*x^22 + 78*x^21 + 52*x^20 + 19*x^19 + 104*x^18 + 27*x^17 + 54*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 86*x^8 + 70*x^7 + 40*x^6 + 94*x^5 + 52*x^4 + 117*x^3 + 8*x^2 + 29*x + 106, x^27 + 33*x^25 + 34*x^24 + 38*x^23 + 104*x^22 + 62*x^21 + 68*x^20 + 67*x^19 + 72*x^18 + 107*x^17 + 62*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 62*x^8 + 22*x^7 + 72*x^6 + 14*x^5 + 68*x^4 + 101*x^3 + 104*x^2 + 45*x + 34, x^27 + 33*x^25 + 18*x^24 + 86*x^23 + 88*x^22 + 110*x^21 + 20*x^20 + 19*x^19 + 88*x^18 + 59*x^17 + 94*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 110*x^8 + 6*x^7 + 120*x^6 + 126*x^5 + 84*x^4 + 117*x^3 + 56*x^2 + 61*x + 98, x^27 + 33*x^25 + 42*x^24 + 70*x^23 + 120*x^22 + 62*x^21 + 36*x^20 + 99*x^19 + 56*x^18 + 43*x^17 + 38*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 22*x^8 + 54*x^7 + 24*x^6 + 14*x^5 + 100*x^4 + 5*x^3 + 24*x^2 + 109*x + 90, x^27 + 33*x^25 + 90*x^24 + 54*x^23 + 8*x^22 + 110*x^21 + 84*x^20 + 115*x^19 + 40*x^18 + 123*x^17 + 38*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 70*x^8 + 102*x^7 + 104*x^6 + 126*x^5 + 84*x^4 + 85*x^3 + 72*x^2 + 125*x + 122, x^27 + 33*x^25 + 30*x^24 + 6*x^23 + 56*x^22 + 94*x^21 + 28*x^20 + 99*x^19 + 24*x^18 + 75*x^17 + 34*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 66*x^8 + 118*x^7 + 88*x^6 + 46*x^5 + 28*x^4 + 5*x^3 + 120*x^2 + 13*x + 62, x^27 + 33*x^25 + 94*x^24 + 22*x^23 + 8*x^22 + 46*x^21 + 108*x^20 + 83*x^19 + 72*x^18 + 123*x^17 + 18*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 98*x^8 + 70*x^7 + 104*x^6 + 62*x^5 + 44*x^4 + 53*x^3 + 104*x^2 + 125*x + 110, x^27 + 33*x^25 + 122*x^24 + 86*x^23 + 104*x^22 + 78*x^21 + 52*x^20 + 83*x^19 + 72*x^18 + 27*x^17 + 102*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 102*x^8 + 6*x^7 + 72*x^6 + 94*x^5 + 52*x^4 + 53*x^3 + 104*x^2 + 29*x + 122, x^27 + 33*x^25 + 42*x^24 + 38*x^23 + 56*x^22 + 30*x^21 + 100*x^20 + 3*x^19 + 120*x^18 + 75*x^17 + 102*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 22*x^8 + 22*x^7 + 88*x^6 + 110*x^5 + 36*x^4 + 37*x^3 + 88*x^2 + 13*x + 26, x^27 + 33*x^25 + 22*x^24 + 54*x^23 + 56*x^22 + 110*x^21 + 12*x^20 + 115*x^19 + 24*x^18 + 123*x^17 + 106*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 74*x^8 + 102*x^7 + 88*x^6 + 126*x^5 + 12*x^4 + 85*x^3 + 120*x^2 + 125*x + 118, x^27 + 33*x^25 + 26*x^24 + 102*x^23 + 88*x^22 + 94*x^21 + 36*x^20 + 67*x^19 + 88*x^18 + 11*x^17 + 22*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 102*x^8 + 86*x^7 + 120*x^6 + 46*x^5 + 100*x^4 + 101*x^3 + 56*x^2 + 77*x + 42, x^27 + 33*x^25 + 66*x^24 + 54*x^23 + 120*x^22 + 78*x^21 + 84*x^20 + 51*x^19 + 56*x^18 + 91*x^17 + 78*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 126*x^8 + 102*x^7 + 24*x^6 + 94*x^5 + 20*x^4 + 21*x^3 + 24*x^2 + 93*x + 50, x^27 + 33*x^25 + 90*x^24 + 22*x^23 + 72*x^22 + 14*x^21 + 84*x^20 + 19*x^19 + 104*x^18 + 91*x^17 + 38*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 70*x^8 + 70*x^7 + 40*x^6 + 30*x^5 + 84*x^4 + 117*x^3 + 8*x^2 + 93*x + 122, x^27 + 33*x^25 + 54*x^24 + 70*x^23 + 8*x^22 + 62*x^21 + 28*x^20 + 99*x^19 + 72*x^18 + 43*x^17 + 122*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 10*x^8 + 54*x^7 + 104*x^6 + 14*x^5 + 92*x^4 + 5*x^3 + 104*x^2 + 109*x + 6, x^27 + 33*x^25 + 46*x^24 + 38*x^23 + 120*x^22 + 126*x^21 + 60*x^20 + 67*x^19 + 88*x^18 + 43*x^17 + 18*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 50*x^8 + 22*x^7 + 24*x^6 + 78*x^5 + 60*x^4 + 101*x^3 + 56*x^2 + 109*x + 78, x^27 + 33*x^25 + 114*x^24 + 54*x^23 + 56*x^22 + 14*x^21 + 116*x^20 + 51*x^19 + 120*x^18 + 27*x^17 + 94*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 78*x^8 + 102*x^7 + 88*x^6 + 30*x^5 + 52*x^4 + 21*x^3 + 88*x^2 + 29*x + 34, x^27 + 33*x^25 + 38*x^24 + 70*x^23 + 104*x^22 + 62*x^21 + 28*x^20 + 99*x^19 + 104*x^18 + 43*x^17 + 106*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 90*x^8 + 54*x^7 + 72*x^6 + 14*x^5 + 92*x^4 + 5*x^3 + 8*x^2 + 109*x + 86, x^27 + 33*x^25 + 110*x^24 + 54*x^23 + 40*x^22 + 78*x^21 + 108*x^20 + 51*x^19 + 40*x^18 + 91*x^17 + 34*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 18*x^8 + 102*x^7 + 8*x^6 + 94*x^5 + 44*x^4 + 21*x^3 + 72*x^2 + 93*x + 30, x^27 + 33*x^25 + 50*x^24 + 54*x^23 + 56*x^22 + 78*x^21 + 52*x^20 + 51*x^19 + 120*x^18 + 91*x^17 + 94*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 14*x^8 + 102*x^7 + 88*x^6 + 94*x^5 + 116*x^4 + 21*x^3 + 88*x^2 + 93*x + 34, x^27 + 33*x^25 + 86*x^24 + 6*x^23 + 104*x^22 + 126*x^21 + 60*x^20 + 35*x^19 + 104*x^18 + 107*x^17 + 122*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 42*x^8 + 118*x^7 + 72*x^6 + 78*x^5 + 124*x^4 + 69*x^3 + 8*x^2 + 45*x + 70, x^27 + 33*x^25 + 110*x^24 + 54*x^23 + 104*x^22 + 14*x^21 + 108*x^20 + 51*x^19 + 104*x^18 + 27*x^17 + 34*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 18*x^8 + 102*x^7 + 72*x^6 + 30*x^5 + 44*x^4 + 21*x^3 + 8*x^2 + 29*x + 30, x^27 + 33*x^25 + 22*x^24 + 6*x^23 + 40*x^22 + 62*x^21 + 60*x^20 + 35*x^19 + 40*x^18 + 43*x^17 + 58*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 106*x^8 + 118*x^7 + 8*x^6 + 14*x^5 + 124*x^4 + 69*x^3 + 72*x^2 + 109*x + 6, x^27 + 33*x^25 + 30*x^24 + 86*x^23 + 8*x^22 + 110*x^21 + 108*x^20 + 19*x^19 + 72*x^18 + 59*x^17 + 82*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 34*x^8 + 6*x^7 + 104*x^6 + 126*x^5 + 44*x^4 + 117*x^3 + 104*x^2 + 61*x + 46, x^27 + 33*x^25 + 58*x^24 + 54*x^23 + 8*x^22 + 110*x^21 + 20*x^20 + 115*x^19 + 40*x^18 + 123*x^17 + 70*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 102*x^8 + 102*x^7 + 104*x^6 + 126*x^5 + 20*x^4 + 85*x^3 + 72*x^2 + 125*x + 90, x^27 + 33*x^25 + 74*x^24 + 54*x^23 + 104*x^22 + 46*x^21 + 20*x^20 + 115*x^19 + 72*x^18 + 59*x^17 + 86*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 22*x^8 + 102*x^7 + 72*x^6 + 62*x^5 + 20*x^4 + 85*x^3 + 104*x^2 + 61*x + 10, x^27 + 33*x^25 + 90*x^24 + 118*x^23 + 72*x^22 + 110*x^21 + 84*x^20 + 51*x^19 + 104*x^18 + 123*x^17 + 38*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 70*x^8 + 38*x^7 + 40*x^6 + 126*x^5 + 84*x^4 + 21*x^3 + 8*x^2 + 125*x + 122, x^27 + 33*x^25 + 38*x^24 + 102*x^23 + 40*x^22 + 94*x^21 + 92*x^20 + 67*x^19 + 40*x^18 + 11*x^17 + 42*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 90*x^8 + 86*x^7 + 8*x^6 + 46*x^5 + 28*x^4 + 101*x^3 + 72*x^2 + 77*x + 22, x^27 + 33*x^25 + 2*x^24 + 86*x^23 + 120*x^22 + 110*x^21 + 84*x^20 + 19*x^19 + 56*x^18 + 59*x^17 + 14*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 62*x^8 + 6*x^7 + 24*x^6 + 126*x^5 + 20*x^4 + 117*x^3 + 24*x^2 + 61*x + 114, x^27 + 33*x^25 + 50*x^24 + 6*x^23 + 72*x^22 + 30*x^21 + 4*x^20 + 99*x^19 + 104*x^18 + 11*x^17 + 14*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 110*x^8 + 118*x^7 + 40*x^6 + 110*x^5 + 4*x^4 + 5*x^3 + 8*x^2 + 77*x + 18, x^27 + 33*x^25 + 22*x^24 + 38*x^23 + 104*x^22 + 30*x^21 + 60*x^20 + 3*x^19 + 104*x^18 + 75*x^17 + 58*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 106*x^8 + 22*x^7 + 72*x^6 + 110*x^5 + 124*x^4 + 37*x^3 + 8*x^2 + 13*x + 6, x^27 + 33*x^25 + 26*x^24 + 38*x^23 + 56*x^22 + 94*x^21 + 68*x^20 + 3*x^19 + 120*x^18 + 11*x^17 + 118*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 38*x^8 + 22*x^7 + 88*x^6 + 46*x^5 + 4*x^4 + 37*x^3 + 88*x^2 + 77*x + 10, x^27 + 33*x^25 + 86*x^24 + 118*x^23 + 56*x^22 + 46*x^21 + 12*x^20 + 51*x^19 + 24*x^18 + 59*x^17 + 42*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 10*x^8 + 38*x^7 + 88*x^6 + 62*x^5 + 12*x^4 + 21*x^3 + 120*x^2 + 61*x + 54, x^27 + 33*x^25 + 34*x^24 + 54*x^23 + 88*x^22 + 78*x^21 + 116*x^20 + 51*x^19 + 88*x^18 + 91*x^17 + 14*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 94*x^8 + 102*x^7 + 120*x^6 + 94*x^5 + 52*x^4 + 21*x^3 + 56*x^2 + 93*x + 50, x^27 + 33*x^25 + 98*x^24 + 118*x^23 + 24*x^22 + 14*x^21 + 52*x^20 + 115*x^19 + 24*x^18 + 27*x^17 + 14*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 30*x^8 + 38*x^7 + 56*x^6 + 30*x^5 + 116*x^4 + 85*x^3 + 120*x^2 + 29*x + 50, x^27 + 33*x^25 + 54*x^24 + 102*x^23 + 104*x^22 + 94*x^21 + 124*x^20 + 67*x^19 + 104*x^18 + 11*x^17 + 26*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 74*x^8 + 86*x^7 + 72*x^6 + 46*x^5 + 60*x^4 + 101*x^3 + 8*x^2 + 77*x + 38, x^27 + 33*x^25 + 62*x^24 + 54*x^23 + 8*x^22 + 78*x^21 + 44*x^20 + 51*x^19 + 72*x^18 + 91*x^17 + 50*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 2*x^8 + 102*x^7 + 104*x^6 + 94*x^5 + 108*x^4 + 21*x^3 + 104*x^2 + 93*x + 78, x^27 + 33*x^25 + 126*x^24 + 54*x^23 + 40*x^22 + 78*x^21 + 76*x^20 + 51*x^19 + 40*x^18 + 91*x^17 + 82*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 2*x^8 + 102*x^7 + 8*x^6 + 94*x^5 + 12*x^4 + 21*x^3 + 72*x^2 + 93*x + 110, x^27 + 33*x^25 + 126*x^24 + 70*x^23 + 88*x^22 + 30*x^21 + 124*x^20 + 35*x^19 + 120*x^18 + 11*x^17 + 34*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 34*x^8 + 54*x^7 + 120*x^6 + 110*x^5 + 124*x^4 + 69*x^3 + 88*x^2 + 77*x + 126, x^27 + 33*x^25 + 126*x^24 + 54*x^23 + 104*x^22 + 14*x^21 + 76*x^20 + 51*x^19 + 104*x^18 + 27*x^17 + 82*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 2*x^8 + 102*x^7 + 72*x^6 + 30*x^5 + 12*x^4 + 21*x^3 + 8*x^2 + 29*x + 110, x^27 + 33*x^25 + 50*x^24 + 70*x^23 + 104*x^22 + 30*x^21 + 100*x^20 + 35*x^19 + 72*x^18 + 11*x^17 + 46*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 46*x^8 + 54*x^7 + 72*x^6 + 110*x^5 + 100*x^4 + 69*x^3 + 104*x^2 + 77*x + 50, x^27 + 33*x^25 + 106*x^24 + 118*x^23 + 40*x^22 + 46*x^21 + 84*x^20 + 51*x^19 + 8*x^18 + 59*x^17 + 54*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 118*x^8 + 38*x^7 + 8*x^6 + 62*x^5 + 84*x^4 + 21*x^3 + 40*x^2 + 61*x + 42, x^27 + 33*x^25 + 78*x^24 + 22*x^23 + 104*x^22 + 46*x^21 + 108*x^20 + 83*x^19 + 104*x^18 + 123*x^17 + 2*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 50*x^8 + 70*x^7 + 72*x^6 + 62*x^5 + 44*x^4 + 53*x^3 + 8*x^2 + 125*x + 62, x^27 + 33*x^25 + 18*x^24 + 54*x^23 + 56*x^22 + 14*x^21 + 52*x^20 + 51*x^19 + 120*x^18 + 27*x^17 + 62*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 46*x^8 + 102*x^7 + 88*x^6 + 30*x^5 + 116*x^4 + 21*x^3 + 88*x^2 + 29*x + 66, x^27 + 33*x^25 + 34*x^24 + 102*x^23 + 8*x^22 + 126*x^21 + 100*x^20 + 3*x^19 + 40*x^18 + 43*x^17 + 30*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 126*x^8 + 86*x^7 + 104*x^6 + 78*x^5 + 100*x^4 + 37*x^3 + 72*x^2 + 109*x + 2, x^27 + 33*x^25 + 34*x^24 + 54*x^23 + 24*x^22 + 14*x^21 + 116*x^20 + 51*x^19 + 24*x^18 + 27*x^17 + 14*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 94*x^8 + 102*x^7 + 56*x^6 + 30*x^5 + 52*x^4 + 21*x^3 + 120*x^2 + 29*x + 50, x^27 + 33*x^25 + 82*x^24 + 38*x^23 + 8*x^22 + 62*x^21 + 4*x^20 + 67*x^19 + 40*x^18 + 107*x^17 + 46*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 78*x^8 + 22*x^7 + 104*x^6 + 14*x^5 + 4*x^4 + 101*x^3 + 72*x^2 + 45*x + 114, x^27 + 33*x^25 + 98*x^24 + 38*x^23 + 8*x^22 + 126*x^21 + 36*x^20 + 67*x^19 + 40*x^18 + 43*x^17 + 30*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 62*x^8 + 22*x^7 + 104*x^6 + 78*x^5 + 36*x^4 + 101*x^3 + 72*x^2 + 109*x + 2, x^27 + 33*x^25 + 58*x^24 + 22*x^23 + 72*x^22 + 14*x^21 + 20*x^20 + 19*x^19 + 104*x^18 + 91*x^17 + 70*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 102*x^8 + 70*x^7 + 40*x^6 + 30*x^5 + 20*x^4 + 117*x^3 + 8*x^2 + 93*x + 90, x^27 + 33*x^25 + 98*x^24 + 102*x^23 + 8*x^22 + 62*x^21 + 36*x^20 + 3*x^19 + 40*x^18 + 107*x^17 + 30*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 62*x^8 + 86*x^7 + 104*x^6 + 14*x^5 + 36*x^4 + 37*x^3 + 72*x^2 + 45*x + 2, x^27 + 33*x^25 + 62*x^24 + 118*x^23 + 8*x^22 + 14*x^21 + 44*x^20 + 115*x^19 + 72*x^18 + 27*x^17 + 50*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 2*x^8 + 38*x^7 + 104*x^6 + 30*x^5 + 108*x^4 + 85*x^3 + 104*x^2 + 29*x + 78, x^27 + 33*x^25 + 82*x^24 + 86*x^23 + 120*x^22 + 46*x^21 + 116*x^20 + 19*x^19 + 56*x^18 + 123*x^17 + 62*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 110*x^8 + 6*x^7 + 24*x^6 + 62*x^5 + 52*x^4 + 117*x^3 + 24*x^2 + 125*x + 66, x^27 + 33*x^25 + 98*x^24 + 6*x^23 + 8*x^22 + 94*x^21 + 36*x^20 + 99*x^19 + 40*x^18 + 75*x^17 + 30*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 62*x^8 + 118*x^7 + 104*x^6 + 46*x^5 + 36*x^4 + 5*x^3 + 72*x^2 + 13*x + 2, x^27 + 33*x^25 + 98*x^24 + 102*x^23 + 40*x^22 + 62*x^21 + 68*x^20 + 3*x^19 + 8*x^18 + 107*x^17 + 126*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 126*x^8 + 86*x^7 + 8*x^6 + 14*x^5 + 68*x^4 + 37*x^3 + 40*x^2 + 45*x + 98, x^27 + 33*x^25 + 90*x^24 + 102*x^23 + 88*x^22 + 30*x^21 + 100*x^20 + 67*x^19 + 88*x^18 + 75*x^17 + 22*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 38*x^8 + 86*x^7 + 120*x^6 + 110*x^5 + 36*x^4 + 101*x^3 + 56*x^2 + 13*x + 42, x^27 + 33*x^25 + 22*x^24 + 38*x^23 + 104*x^22 + 94*x^21 + 124*x^20 + 3*x^19 + 104*x^18 + 11*x^17 + 122*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 106*x^8 + 22*x^7 + 72*x^6 + 46*x^5 + 60*x^4 + 37*x^3 + 8*x^2 + 77*x + 70, x^27 + 33*x^25 + 26*x^24 + 118*x^23 + 104*x^22 + 110*x^21 + 116*x^20 + 51*x^19 + 72*x^18 + 123*x^17 + 70*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 70*x^8 + 38*x^7 + 72*x^6 + 126*x^5 + 116*x^4 + 21*x^3 + 104*x^2 + 125*x + 26, x^27 + 33*x^25 + 74*x^24 + 86*x^23 + 72*x^22 + 78*x^21 + 116*x^20 + 83*x^19 + 104*x^18 + 27*x^17 + 118*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 86*x^8 + 6*x^7 + 40*x^6 + 94*x^5 + 116*x^4 + 53*x^3 + 8*x^2 + 29*x + 42, x^27 + 33*x^25 + 54*x^24 + 70*x^23 + 72*x^22 + 126*x^21 + 28*x^20 + 99*x^19 + 8*x^18 + 107*x^17 + 122*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 10*x^8 + 54*x^7 + 40*x^6 + 78*x^5 + 92*x^4 + 5*x^3 + 40*x^2 + 45*x + 6, x^27 + 33*x^25 + 2*x^24 + 22*x^23 + 24*x^22 + 46*x^21 + 116*x^20 + 83*x^19 + 24*x^18 + 123*x^17 + 110*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 126*x^8 + 70*x^7 + 56*x^6 + 62*x^5 + 52*x^4 + 53*x^3 + 120*x^2 + 125*x + 82, x^27 + 33*x^25 + 94*x^24 + 70*x^23 + 24*x^22 + 94*x^21 + 60*x^20 + 35*x^19 + 56*x^18 + 75*x^17 + 66*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 66*x^8 + 54*x^7 + 56*x^6 + 46*x^5 + 60*x^4 + 69*x^3 + 24*x^2 + 13*x + 94, x^27 + 33*x^25 + 90*x^24 + 102*x^23 + 24*x^22 + 94*x^21 + 100*x^20 + 67*x^19 + 24*x^18 + 11*x^17 + 22*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 38*x^8 + 86*x^7 + 56*x^6 + 46*x^5 + 36*x^4 + 101*x^3 + 120*x^2 + 77*x + 42, x^27 + 33*x^25 + 10*x^24 + 54*x^23 + 104*x^22 + 110*x^21 + 84*x^20 + 115*x^19 + 72*x^18 + 123*x^17 + 86*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 86*x^8 + 102*x^7 + 72*x^6 + 126*x^5 + 84*x^4 + 85*x^3 + 104*x^2 + 125*x + 10, x^27 + 33*x^25 + 14*x^24 + 6*x^23 + 24*x^22 + 94*x^21 + 28*x^20 + 99*x^19 + 56*x^18 + 75*x^17 + 18*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 18*x^8 + 118*x^7 + 56*x^6 + 46*x^5 + 28*x^4 + 5*x^3 + 24*x^2 + 13*x + 14, x^27 + 33*x^25 + 82*x^24 + 6*x^23 + 104*x^22 + 30*x^21 + 100*x^20 + 99*x^19 + 72*x^18 + 11*x^17 + 78*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 14*x^8 + 118*x^7 + 72*x^6 + 110*x^5 + 100*x^4 + 5*x^3 + 104*x^2 + 77*x + 18, x^27 + 33*x^25 + 102*x^24 + 70*x^23 + 40*x^22 + 62*x^21 + 92*x^20 + 99*x^19 + 40*x^18 + 43*x^17 + 106*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 26*x^8 + 54*x^7 + 8*x^6 + 14*x^5 + 28*x^4 + 5*x^3 + 72*x^2 + 109*x + 86, x^27 + 33*x^25 + 62*x^24 + 6*x^23 + 24*x^22 + 94*x^21 + 60*x^20 + 99*x^19 + 56*x^18 + 75*x^17 + 34*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 98*x^8 + 118*x^7 + 56*x^6 + 46*x^5 + 60*x^4 + 5*x^3 + 24*x^2 + 13*x + 126, x^27 + 33*x^25 + 114*x^24 + 38*x^23 + 8*x^22 + 126*x^21 + 4*x^20 + 67*x^19 + 40*x^18 + 43*x^17 + 78*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 46*x^8 + 22*x^7 + 104*x^6 + 78*x^5 + 4*x^4 + 101*x^3 + 72*x^2 + 109*x + 82, x^27 + 33*x^25 + 6*x^24 + 38*x^23 + 40*x^22 + 94*x^21 + 92*x^20 + 3*x^19 + 40*x^18 + 11*x^17 + 10*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 122*x^8 + 22*x^7 + 8*x^6 + 46*x^5 + 28*x^4 + 37*x^3 + 72*x^2 + 77*x + 54, x^27 + 33*x^25 + 38*x^24 + 22*x^23 + 24*x^22 + 14*x^21 + 12*x^20 + 19*x^19 + 56*x^18 + 91*x^17 + 122*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 122*x^8 + 70*x^7 + 56*x^6 + 30*x^5 + 12*x^4 + 117*x^3 + 24*x^2 + 93*x + 38, x^27 + 33*x^25 + 126*x^24 + 38*x^23 + 88*x^22 + 126*x^21 + 124*x^20 + 67*x^19 + 120*x^18 + 43*x^17 + 34*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 34*x^8 + 22*x^7 + 120*x^6 + 78*x^5 + 124*x^4 + 101*x^3 + 88*x^2 + 109*x + 126, x^27 + 33*x^25 + 78*x^24 + 22*x^23 + 8*x^22 + 110*x^21 + 76*x^20 + 83*x^19 + 72*x^18 + 59*x^17 + 34*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 114*x^8 + 70*x^7 + 104*x^6 + 126*x^5 + 12*x^4 + 53*x^3 + 104*x^2 + 61*x + 94, x^27 + 33*x^25 + 114*x^24 + 102*x^23 + 8*x^22 + 62*x^21 + 4*x^20 + 3*x^19 + 40*x^18 + 107*x^17 + 78*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 46*x^8 + 86*x^7 + 104*x^6 + 14*x^5 + 4*x^4 + 37*x^3 + 72*x^2 + 45*x + 82, x^27 + 33*x^25 + 94*x^24 + 6*x^23 + 24*x^22 + 94*x^21 + 124*x^20 + 99*x^19 + 56*x^18 + 75*x^17 + 2*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 66*x^8 + 118*x^7 + 56*x^6 + 46*x^5 + 124*x^4 + 5*x^3 + 24*x^2 + 13*x + 30, x^27 + 33*x^25 + 126*x^24 + 102*x^23 + 88*x^22 + 62*x^21 + 124*x^20 + 3*x^19 + 120*x^18 + 107*x^17 + 34*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 34*x^8 + 86*x^7 + 120*x^6 + 14*x^5 + 124*x^4 + 37*x^3 + 88*x^2 + 45*x + 126, x^27 + 33*x^25 + 94*x^24 + 6*x^23 + 120*x^22 + 94*x^21 + 92*x^20 + 99*x^19 + 88*x^18 + 75*x^17 + 34*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 2*x^8 + 118*x^7 + 24*x^6 + 46*x^5 + 92*x^4 + 5*x^3 + 56*x^2 + 13*x + 62, x^27 + 33*x^25 + 86*x^24 + 102*x^23 + 8*x^22 + 94*x^21 + 92*x^20 + 67*x^19 + 72*x^18 + 11*x^17 + 90*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 106*x^8 + 86*x^7 + 104*x^6 + 46*x^5 + 28*x^4 + 101*x^3 + 104*x^2 + 77*x + 38, x^27 + 33*x^25 + 58*x^24 + 86*x^23 + 72*x^22 + 78*x^21 + 20*x^20 + 83*x^19 + 104*x^18 + 27*x^17 + 70*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 102*x^8 + 6*x^7 + 40*x^6 + 94*x^5 + 20*x^4 + 53*x^3 + 8*x^2 + 29*x + 90, x^27 + 33*x^25 + 30*x^24 + 6*x^23 + 120*x^22 + 30*x^21 + 28*x^20 + 99*x^19 + 88*x^18 + 11*x^17 + 34*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 66*x^8 + 118*x^7 + 24*x^6 + 110*x^5 + 28*x^4 + 5*x^3 + 56*x^2 + 77*x + 62, x^27 + 33*x^25 + 38*x^24 + 86*x^23 + 120*x^22 + 14*x^21 + 44*x^20 + 83*x^19 + 88*x^18 + 91*x^17 + 90*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 58*x^8 + 6*x^7 + 24*x^6 + 30*x^5 + 44*x^4 + 53*x^3 + 56*x^2 + 93*x + 6, x^27 + 33*x^25 + 22*x^24 + 22*x^23 + 24*x^22 + 78*x^21 + 108*x^20 + 19*x^19 + 56*x^18 + 27*x^17 + 10*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 10*x^8 + 70*x^7 + 56*x^6 + 94*x^5 + 108*x^4 + 117*x^3 + 24*x^2 + 29*x + 22, x^27 + 33*x^25 + 98*x^24 + 6*x^23 + 104*x^22 + 30*x^21 + 68*x^20 + 99*x^19 + 72*x^18 + 11*x^17 + 126*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 126*x^8 + 118*x^7 + 72*x^6 + 110*x^5 + 68*x^4 + 5*x^3 + 104*x^2 + 77*x + 98, x^27 + 33*x^25 + 62*x^24 + 86*x^23 + 8*x^22 + 110*x^21 + 44*x^20 + 19*x^19 + 72*x^18 + 59*x^17 + 50*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 2*x^8 + 6*x^7 + 104*x^6 + 126*x^5 + 108*x^4 + 117*x^3 + 104*x^2 + 61*x + 78, x^27 + 33*x^25 + 126*x^24 + 86*x^23 + 40*x^22 + 110*x^21 + 76*x^20 + 19*x^19 + 40*x^18 + 59*x^17 + 82*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 2*x^8 + 6*x^7 + 8*x^6 + 126*x^5 + 12*x^4 + 117*x^3 + 72*x^2 + 61*x + 110, x^27 + 33*x^25 + 122*x^24 + 6*x^23 + 56*x^22 + 126*x^21 + 68*x^20 + 35*x^19 + 120*x^18 + 107*x^17 + 86*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 70*x^8 + 118*x^7 + 88*x^6 + 78*x^5 + 4*x^4 + 69*x^3 + 88*x^2 + 45*x + 42, x^27 + 33*x^25 + 106*x^24 + 38*x^23 + 88*x^22 + 30*x^21 + 4*x^20 + 3*x^19 + 88*x^18 + 75*x^17 + 6*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 22*x^8 + 22*x^7 + 120*x^6 + 110*x^5 + 68*x^4 + 37*x^3 + 56*x^2 + 13*x + 58, x^27 + 33*x^25 + 126*x^24 + 118*x^23 + 72*x^22 + 78*x^21 + 44*x^20 + 115*x^19 + 8*x^18 + 91*x^17 + 114*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 66*x^8 + 38*x^7 + 40*x^6 + 94*x^5 + 108*x^4 + 85*x^3 + 40*x^2 + 93*x + 14, x^27 + 33*x^25 + 54*x^24 + 6*x^23 + 72*x^22 + 62*x^21 + 28*x^20 + 35*x^19 + 8*x^18 + 43*x^17 + 122*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 10*x^8 + 118*x^7 + 40*x^6 + 14*x^5 + 92*x^4 + 69*x^3 + 40*x^2 + 109*x + 6, x^27 + 33*x^25 + 18*x^24 + 22*x^23 + 88*x^22 + 46*x^21 + 20*x^20 + 83*x^19 + 88*x^18 + 123*x^17 + 94*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 110*x^8 + 70*x^7 + 120*x^6 + 62*x^5 + 84*x^4 + 53*x^3 + 56*x^2 + 125*x + 98, x^27 + 33*x^25 + 106*x^24 + 38*x^23 + 24*x^22 + 94*x^21 + 4*x^20 + 3*x^19 + 24*x^18 + 11*x^17 + 6*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 22*x^8 + 22*x^7 + 56*x^6 + 46*x^5 + 68*x^4 + 37*x^3 + 120*x^2 + 77*x + 58, x^27 + 33*x^25 + 86*x^24 + 6*x^23 + 40*x^22 + 62*x^21 + 60*x^20 + 35*x^19 + 40*x^18 + 43*x^17 + 122*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 42*x^8 + 118*x^7 + 8*x^6 + 14*x^5 + 124*x^4 + 69*x^3 + 72*x^2 + 109*x + 70, x^27 + 33*x^25 + 126*x^24 + 6*x^23 + 56*x^22 + 30*x^21 + 28*x^20 + 99*x^19 + 24*x^18 + 11*x^17 + 2*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 98*x^8 + 118*x^7 + 88*x^6 + 110*x^5 + 28*x^4 + 5*x^3 + 120*x^2 + 77*x + 94, x^27 + 33*x^25 + 118*x^24 + 6*x^23 + 8*x^22 + 126*x^21 + 28*x^20 + 35*x^19 + 72*x^18 + 107*x^17 + 58*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 74*x^8 + 118*x^7 + 104*x^6 + 78*x^5 + 92*x^4 + 69*x^3 + 104*x^2 + 45*x + 70, x^27 + 33*x^25 + 46*x^24 + 54*x^23 + 40*x^22 + 78*x^21 + 108*x^20 + 51*x^19 + 40*x^18 + 91*x^17 + 98*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 82*x^8 + 102*x^7 + 8*x^6 + 94*x^5 + 44*x^4 + 21*x^3 + 72*x^2 + 93*x + 94, x^27 + 33*x^25 + 126*x^24 + 54*x^23 + 104*x^22 + 78*x^21 + 12*x^20 + 51*x^19 + 104*x^18 + 91*x^17 + 18*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 2*x^8 + 102*x^7 + 72*x^6 + 94*x^5 + 76*x^4 + 21*x^3 + 8*x^2 + 93*x + 46, x^27 + 33*x^25 + 102*x^24 + 6*x^23 + 40*x^22 + 126*x^21 + 92*x^20 + 35*x^19 + 40*x^18 + 107*x^17 + 106*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 26*x^8 + 118*x^7 + 8*x^6 + 78*x^5 + 28*x^4 + 69*x^3 + 72*x^2 + 45*x + 86, x^27 + 33*x^25 + 46*x^24 + 54*x^23 + 104*x^22 + 14*x^21 + 108*x^20 + 51*x^19 + 104*x^18 + 27*x^17 + 98*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 82*x^8 + 102*x^7 + 72*x^6 + 30*x^5 + 44*x^4 + 21*x^3 + 8*x^2 + 29*x + 94, x^27 + 33*x^25 + 14*x^24 + 38*x^23 + 120*x^22 + 62*x^21 + 60*x^20 + 67*x^19 + 88*x^18 + 107*x^17 + 114*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 82*x^8 + 22*x^7 + 24*x^6 + 14*x^5 + 60*x^4 + 101*x^3 + 56*x^2 + 45*x + 110, x^27 + 33*x^25 + 50*x^24 + 38*x^23 + 72*x^22 + 62*x^21 + 4*x^20 + 67*x^19 + 104*x^18 + 107*x^17 + 14*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 110*x^8 + 22*x^7 + 40*x^6 + 14*x^5 + 4*x^4 + 101*x^3 + 8*x^2 + 45*x + 18, x^27 + 33*x^25 + 46*x^24 + 38*x^23 + 88*x^22 + 126*x^21 + 28*x^20 + 67*x^19 + 120*x^18 + 43*x^17 + 50*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 114*x^8 + 22*x^7 + 120*x^6 + 78*x^5 + 28*x^4 + 101*x^3 + 88*x^2 + 109*x + 110, x^27 + 33*x^25 + 106*x^24 + 22*x^23 + 72*x^22 + 14*x^21 + 52*x^20 + 19*x^19 + 104*x^18 + 91*x^17 + 86*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 54*x^8 + 70*x^7 + 40*x^6 + 30*x^5 + 52*x^4 + 117*x^3 + 8*x^2 + 93*x + 74, x^27 + 33*x^25 + 86*x^24 + 38*x^23 + 104*x^22 + 30*x^21 + 60*x^20 + 3*x^19 + 104*x^18 + 75*x^17 + 122*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 42*x^8 + 22*x^7 + 72*x^6 + 110*x^5 + 124*x^4 + 37*x^3 + 8*x^2 + 13*x + 70, x^27 + 33*x^25 + 98*x^24 + 86*x^23 + 88*x^22 + 110*x^21 + 116*x^20 + 19*x^19 + 88*x^18 + 59*x^17 + 78*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 30*x^8 + 6*x^7 + 120*x^6 + 126*x^5 + 52*x^4 + 117*x^3 + 56*x^2 + 61*x + 114, x^27 + 33*x^25 + 126*x^24 + 102*x^23 + 120*x^22 + 126*x^21 + 92*x^20 + 3*x^19 + 88*x^18 + 43*x^17 + 66*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 98*x^8 + 86*x^7 + 24*x^6 + 78*x^5 + 92*x^4 + 37*x^3 + 56*x^2 + 109*x + 30, x^27 + 33*x^25 + 42*x^24 + 22*x^23 + 72*x^22 + 78*x^21 + 116*x^20 + 19*x^19 + 104*x^18 + 27*x^17 + 86*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 118*x^8 + 70*x^7 + 40*x^6 + 94*x^5 + 116*x^4 + 117*x^3 + 8*x^2 + 29*x + 74, x^27 + 33*x^25 + 54*x^24 + 38*x^23 + 104*x^22 + 30*x^21 + 124*x^20 + 3*x^19 + 104*x^18 + 75*x^17 + 26*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 74*x^8 + 22*x^7 + 72*x^6 + 110*x^5 + 60*x^4 + 37*x^3 + 8*x^2 + 13*x + 38, x^27 + 33*x^25 + 70*x^24 + 6*x^23 + 40*x^22 + 126*x^21 + 28*x^20 + 35*x^19 + 40*x^18 + 107*x^17 + 10*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 58*x^8 + 118*x^7 + 8*x^6 + 78*x^5 + 92*x^4 + 69*x^3 + 72*x^2 + 45*x + 54, x^27 + 33*x^25 + 34*x^24 + 22*x^23 + 24*x^22 + 46*x^21 + 52*x^20 + 83*x^19 + 24*x^18 + 123*x^17 + 78*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 94*x^8 + 70*x^7 + 56*x^6 + 62*x^5 + 116*x^4 + 53*x^3 + 120*x^2 + 125*x + 114, x^27 + 33*x^25 + 122*x^24 + 118*x^23 + 72*x^22 + 46*x^21 + 84*x^20 + 51*x^19 + 104*x^18 + 59*x^17 + 70*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 38*x^8 + 38*x^7 + 40*x^6 + 62*x^5 + 84*x^4 + 21*x^3 + 8*x^2 + 61*x + 90, x^27 + 33*x^25 + 122*x^24 + 6*x^23 + 24*x^22 + 62*x^21 + 100*x^20 + 35*x^19 + 24*x^18 + 43*x^17 + 54*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 6*x^8 + 118*x^7 + 56*x^6 + 14*x^5 + 36*x^4 + 69*x^3 + 120*x^2 + 109*x + 10, x^27 + 33*x^25 + 18*x^24 + 38*x^23 + 104*x^22 + 126*x^21 + 36*x^20 + 67*x^19 + 72*x^18 + 43*x^17 + 78*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 78*x^8 + 22*x^7 + 72*x^6 + 78*x^5 + 36*x^4 + 101*x^3 + 104*x^2 + 109*x + 18, x^27 + 33*x^25 + 74*x^24 + 38*x^23 + 24*x^22 + 94*x^21 + 68*x^20 + 3*x^19 + 24*x^18 + 11*x^17 + 38*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 54*x^8 + 22*x^7 + 56*x^6 + 46*x^5 + 4*x^4 + 37*x^3 + 120*x^2 + 77*x + 26, x^27 + 33*x^25 + 14*x^24 + 86*x^23 + 40*x^22 + 110*x^21 + 44*x^20 + 19*x^19 + 40*x^18 + 59*x^17 + 2*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 114*x^8 + 6*x^7 + 8*x^6 + 126*x^5 + 108*x^4 + 117*x^3 + 72*x^2 + 61*x + 62, x^27 + 33*x^25 + 66*x^24 + 6*x^23 + 104*x^22 + 94*x^21 + 68*x^20 + 99*x^19 + 72*x^18 + 75*x^17 + 94*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 30*x^8 + 118*x^7 + 72*x^6 + 46*x^5 + 68*x^4 + 5*x^3 + 104*x^2 + 13*x + 2, x^27 + 33*x^25 + 66*x^24 + 54*x^23 + 56*x^22 + 14*x^21 + 84*x^20 + 51*x^19 + 120*x^18 + 27*x^17 + 78*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 126*x^8 + 102*x^7 + 88*x^6 + 30*x^5 + 20*x^4 + 21*x^3 + 88*x^2 + 29*x + 50, x^27 + 33*x^25 + 82*x^24 + 54*x^23 + 56*x^22 + 14*x^21 + 52*x^20 + 51*x^19 + 120*x^18 + 27*x^17 + 126*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 110*x^8 + 102*x^7 + 88*x^6 + 30*x^5 + 116*x^4 + 21*x^3 + 88*x^2 + 29*x + 2, x^27 + 33*x^25 + 90*x^24 + 38*x^23 + 88*x^22 + 94*x^21 + 100*x^20 + 3*x^19 + 88*x^18 + 11*x^17 + 22*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 38*x^8 + 22*x^7 + 120*x^6 + 46*x^5 + 36*x^4 + 37*x^3 + 56*x^2 + 77*x + 42, x^27 + 33*x^25 + 82*x^24 + 38*x^23 + 72*x^22 + 62*x^21 + 68*x^20 + 67*x^19 + 104*x^18 + 107*x^17 + 110*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 78*x^8 + 22*x^7 + 40*x^6 + 14*x^5 + 68*x^4 + 101*x^3 + 8*x^2 + 45*x + 50, x^27 + 33*x^25 + 34*x^24 + 38*x^23 + 104*x^22 + 126*x^21 + 4*x^20 + 67*x^19 + 72*x^18 + 43*x^17 + 126*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 62*x^8 + 22*x^7 + 72*x^6 + 78*x^5 + 4*x^4 + 101*x^3 + 104*x^2 + 109*x + 98, x^27 + 33*x^25 + 70*x^24 + 118*x^23 + 120*x^22 + 46*x^21 + 108*x^20 + 51*x^19 + 88*x^18 + 59*x^17 + 58*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 26*x^8 + 38*x^7 + 24*x^6 + 62*x^5 + 108*x^4 + 21*x^3 + 56*x^2 + 61*x + 38, x^27 + 33*x^25 + 102*x^24 + 54*x^23 + 120*x^22 + 110*x^21 + 44*x^20 + 115*x^19 + 88*x^18 + 123*x^17 + 26*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 122*x^8 + 102*x^7 + 24*x^6 + 126*x^5 + 44*x^4 + 85*x^3 + 56*x^2 + 125*x + 70, x^27 + 33*x^25 + 66*x^24 + 86*x^23 + 24*x^22 + 46*x^21 + 52*x^20 + 19*x^19 + 24*x^18 + 123*x^17 + 110*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 62*x^8 + 6*x^7 + 56*x^6 + 62*x^5 + 116*x^4 + 117*x^3 + 120*x^2 + 125*x + 82, x^27 + 33*x^25 + 102*x^24 + 86*x^23 + 56*x^22 + 14*x^21 + 108*x^20 + 83*x^19 + 24*x^18 + 91*x^17 + 90*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 122*x^8 + 6*x^7 + 88*x^6 + 30*x^5 + 108*x^4 + 53*x^3 + 120*x^2 + 93*x + 6, x^27 + 33*x^25 + 42*x^24 + 6*x^23 + 88*x^22 + 62*x^21 + 68*x^20 + 35*x^19 + 88*x^18 + 43*x^17 + 6*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 86*x^8 + 118*x^7 + 120*x^6 + 14*x^5 + 4*x^4 + 69*x^3 + 56*x^2 + 109*x + 58, x^27 + 33*x^25 + 6*x^24 + 70*x^23 + 72*x^22 + 62*x^21 + 60*x^20 + 99*x^19 + 8*x^18 + 43*x^17 + 42*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 58*x^8 + 54*x^7 + 40*x^6 + 14*x^5 + 124*x^4 + 5*x^3 + 40*x^2 + 109*x + 86, x^27 + 33*x^25 + 42*x^24 + 86*x^23 + 104*x^22 + 14*x^21 + 20*x^20 + 83*x^19 + 72*x^18 + 91*x^17 + 54*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 54*x^8 + 6*x^7 + 72*x^6 + 30*x^5 + 20*x^4 + 53*x^3 + 104*x^2 + 93*x + 42, x^27 + 33*x^25 + 22*x^24 + 86*x^23 + 24*x^22 + 14*x^21 + 108*x^20 + 83*x^19 + 56*x^18 + 91*x^17 + 10*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 10*x^8 + 6*x^7 + 56*x^6 + 30*x^5 + 108*x^4 + 53*x^3 + 24*x^2 + 93*x + 22, x^27 + 33*x^25 + 66*x^24 + 54*x^23 + 88*x^22 + 14*x^21 + 116*x^20 + 51*x^19 + 88*x^18 + 27*x^17 + 46*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 62*x^8 + 102*x^7 + 120*x^6 + 30*x^5 + 52*x^4 + 21*x^3 + 56*x^2 + 29*x + 18, x^27 + 33*x^25 + 106*x^24 + 86*x^23 + 72*x^22 + 78*x^21 + 52*x^20 + 83*x^19 + 104*x^18 + 27*x^17 + 86*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 54*x^8 + 6*x^7 + 40*x^6 + 94*x^5 + 52*x^4 + 53*x^3 + 8*x^2 + 29*x + 74, x^27 + 33*x^25 + 102*x^24 + 6*x^23 + 8*x^22 + 126*x^21 + 60*x^20 + 35*x^19 + 72*x^18 + 107*x^17 + 10*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 90*x^8 + 118*x^7 + 104*x^6 + 78*x^5 + 124*x^4 + 69*x^3 + 104*x^2 + 45*x + 118, x^27 + 33*x^25 + 26*x^24 + 102*x^23 + 88*x^22 + 30*x^21 + 100*x^20 + 67*x^19 + 88*x^18 + 75*x^17 + 86*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 102*x^8 + 86*x^7 + 120*x^6 + 110*x^5 + 36*x^4 + 101*x^3 + 56*x^2 + 13*x + 106, x^27 + 33*x^25 + 110*x^24 + 118*x^23 + 8*x^22 + 78*x^21 + 12*x^20 + 115*x^19 + 72*x^18 + 91*x^17 + 2*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 82*x^8 + 38*x^7 + 104*x^6 + 94*x^5 + 76*x^4 + 85*x^3 + 104*x^2 + 93*x + 126, x^27 + 33*x^25 + 74*x^24 + 22*x^23 + 40*x^22 + 14*x^21 + 84*x^20 + 19*x^19 + 8*x^18 + 91*x^17 + 22*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 22*x^8 + 70*x^7 + 8*x^6 + 30*x^5 + 84*x^4 + 117*x^3 + 40*x^2 + 93*x + 74, x^27 + 33*x^25 + 110*x^24 + 38*x^23 + 88*x^22 + 126*x^21 + 28*x^20 + 67*x^19 + 120*x^18 + 43*x^17 + 114*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 50*x^8 + 22*x^7 + 120*x^6 + 78*x^5 + 28*x^4 + 101*x^3 + 88*x^2 + 109*x + 46, x^27 + 33*x^25 + 66*x^24 + 118*x^23 + 56*x^22 + 78*x^21 + 84*x^20 + 115*x^19 + 120*x^18 + 91*x^17 + 78*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 126*x^8 + 38*x^7 + 88*x^6 + 94*x^5 + 20*x^4 + 85*x^3 + 88*x^2 + 93*x + 50, x^27 + 33*x^25 + 110*x^24 + 70*x^23 + 120*x^22 + 30*x^21 + 60*x^20 + 35*x^19 + 88*x^18 + 11*x^17 + 82*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 114*x^8 + 54*x^7 + 24*x^6 + 110*x^5 + 60*x^4 + 69*x^3 + 56*x^2 + 77*x + 14, x^27 + 33*x^25 + 118*x^24 + 22*x^23 + 88*x^22 + 78*x^21 + 108*x^20 + 19*x^19 + 120*x^18 + 27*x^17 + 106*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 42*x^8 + 70*x^7 + 120*x^6 + 94*x^5 + 108*x^4 + 117*x^3 + 88*x^2 + 29*x + 54, x^27 + 33*x^25 + 46*x^24 + 86*x^23 + 40*x^22 + 110*x^21 + 108*x^20 + 19*x^19 + 40*x^18 + 59*x^17 + 98*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 82*x^8 + 6*x^7 + 8*x^6 + 126*x^5 + 44*x^4 + 117*x^3 + 72*x^2 + 61*x + 94, x^27 + 33*x^25 + 2*x^24 + 6*x^23 + 40*x^22 + 30*x^21 + 68*x^20 + 99*x^19 + 8*x^18 + 11*x^17 + 30*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 94*x^8 + 118*x^7 + 8*x^6 + 110*x^5 + 68*x^4 + 5*x^3 + 40*x^2 + 77*x + 66, x^27 + 33*x^25 + 114*x^24 + 86*x^23 + 88*x^22 + 46*x^21 + 20*x^20 + 19*x^19 + 88*x^18 + 123*x^17 + 62*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 14*x^8 + 6*x^7 + 120*x^6 + 62*x^5 + 84*x^4 + 117*x^3 + 56*x^2 + 125*x + 2, x^27 + 33*x^25 + 26*x^24 + 102*x^23 + 24*x^22 + 94*x^21 + 100*x^20 + 67*x^19 + 24*x^18 + 11*x^17 + 86*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 102*x^8 + 86*x^7 + 56*x^6 + 46*x^5 + 36*x^4 + 101*x^3 + 120*x^2 + 77*x + 106, x^27 + 33*x^25 + 114*x^24 + 54*x^23 + 56*x^22 + 78*x^21 + 52*x^20 + 51*x^19 + 120*x^18 + 91*x^17 + 30*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 78*x^8 + 102*x^7 + 88*x^6 + 94*x^5 + 116*x^4 + 21*x^3 + 88*x^2 + 93*x + 98, x^27 + 33*x^25 + 94*x^24 + 38*x^23 + 24*x^22 + 62*x^21 + 60*x^20 + 67*x^19 + 56*x^18 + 107*x^17 + 66*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 66*x^8 + 22*x^7 + 56*x^6 + 14*x^5 + 60*x^4 + 101*x^3 + 24*x^2 + 45*x + 94, x^27 + 33*x^25 + 46*x^24 + 102*x^23 + 56*x^22 + 62*x^21 + 124*x^20 + 3*x^19 + 24*x^18 + 107*x^17 + 82*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 50*x^8 + 86*x^7 + 88*x^6 + 14*x^5 + 124*x^4 + 37*x^3 + 120*x^2 + 45*x + 14, x^27 + 33*x^25 + 10*x^24 + 38*x^23 + 88*x^22 + 30*x^21 + 68*x^20 + 3*x^19 + 88*x^18 + 75*x^17 + 102*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 118*x^8 + 22*x^7 + 120*x^6 + 110*x^5 + 4*x^4 + 37*x^3 + 56*x^2 + 13*x + 90, x^27 + 33*x^25 + 62*x^24 + 54*x^23 + 8*x^22 + 14*x^21 + 108*x^20 + 51*x^19 + 72*x^18 + 27*x^17 + 114*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 2*x^8 + 102*x^7 + 104*x^6 + 30*x^5 + 44*x^4 + 21*x^3 + 104*x^2 + 29*x + 14, x^27 + 33*x^25 + 10*x^24 + 38*x^23 + 88*x^22 + 94*x^21 + 4*x^20 + 3*x^19 + 88*x^18 + 11*x^17 + 38*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 118*x^8 + 22*x^7 + 120*x^6 + 46*x^5 + 68*x^4 + 37*x^3 + 56*x^2 + 77*x + 26, x^27 + 33*x^25 + 114*x^24 + 102*x^23 + 8*x^22 + 126*x^21 + 68*x^20 + 3*x^19 + 40*x^18 + 43*x^17 + 14*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 46*x^8 + 86*x^7 + 104*x^6 + 78*x^5 + 68*x^4 + 37*x^3 + 72*x^2 + 109*x + 18, x^27 + 33*x^25 + 114*x^24 + 6*x^23 + 40*x^22 + 94*x^21 + 36*x^20 + 99*x^19 + 8*x^18 + 75*x^17 + 46*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 110*x^8 + 118*x^7 + 8*x^6 + 46*x^5 + 36*x^4 + 5*x^3 + 40*x^2 + 13*x + 50, x^27 + 33*x^25 + 38*x^24 + 38*x^23 + 8*x^22 + 94*x^21 + 124*x^20 + 3*x^19 + 72*x^18 + 11*x^17 + 10*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 26*x^8 + 22*x^7 + 104*x^6 + 46*x^5 + 60*x^4 + 37*x^3 + 104*x^2 + 77*x + 118, x^27 + 33*x^25 + 86*x^24 + 118*x^23 + 24*x^22 + 46*x^21 + 108*x^20 + 51*x^19 + 56*x^18 + 59*x^17 + 74*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 74*x^8 + 38*x^7 + 56*x^6 + 62*x^5 + 108*x^4 + 21*x^3 + 24*x^2 + 61*x + 86, x^27 + 33*x^25 + 74*x^24 + 118*x^23 + 104*x^22 + 46*x^21 + 84*x^20 + 51*x^19 + 72*x^18 + 59*x^17 + 22*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 22*x^8 + 38*x^7 + 72*x^6 + 62*x^5 + 84*x^4 + 21*x^3 + 104*x^2 + 61*x + 74, x^27 + 33*x^25 + 74*x^24 + 54*x^23 + 8*x^22 + 110*x^21 + 116*x^20 + 115*x^19 + 40*x^18 + 123*x^17 + 118*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 86*x^8 + 102*x^7 + 104*x^6 + 126*x^5 + 116*x^4 + 85*x^3 + 72*x^2 + 125*x + 42, x^27 + 33*x^25 + 42*x^24 + 38*x^23 + 88*x^22 + 30*x^21 + 4*x^20 + 3*x^19 + 88*x^18 + 75*x^17 + 70*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 86*x^8 + 22*x^7 + 120*x^6 + 110*x^5 + 68*x^4 + 37*x^3 + 56*x^2 + 13*x + 122, x^27 + 33*x^25 + 58*x^24 + 70*x^23 + 24*x^22 + 62*x^21 + 36*x^20 + 99*x^19 + 24*x^18 + 43*x^17 + 54*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 70*x^8 + 54*x^7 + 56*x^6 + 14*x^5 + 100*x^4 + 5*x^3 + 120*x^2 + 109*x + 10, x^27 + 33*x^25 + 18*x^24 + 22*x^23 + 24*x^22 + 110*x^21 + 20*x^20 + 83*x^19 + 24*x^18 + 59*x^17 + 94*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 110*x^8 + 70*x^7 + 56*x^6 + 126*x^5 + 84*x^4 + 53*x^3 + 120*x^2 + 61*x + 98, x^27 + 33*x^25 + 74*x^24 + 54*x^23 + 72*x^22 + 46*x^21 + 116*x^20 + 115*x^19 + 104*x^18 + 59*x^17 + 118*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 86*x^8 + 102*x^7 + 40*x^6 + 62*x^5 + 116*x^4 + 85*x^3 + 8*x^2 + 61*x + 42, x^27 + 33*x^25 + 54*x^24 + 102*x^23 + 8*x^22 + 94*x^21 + 28*x^20 + 67*x^19 + 72*x^18 + 11*x^17 + 122*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 10*x^8 + 86*x^7 + 104*x^6 + 46*x^5 + 92*x^4 + 101*x^3 + 104*x^2 + 77*x + 6, x^27 + 33*x^25 + 10*x^24 + 102*x^23 + 88*x^22 + 30*x^21 + 4*x^20 + 67*x^19 + 88*x^18 + 75*x^17 + 38*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 118*x^8 + 86*x^7 + 120*x^6 + 110*x^5 + 68*x^4 + 101*x^3 + 56*x^2 + 13*x + 26, x^27 + 33*x^25 + 78*x^24 + 6*x^23 + 120*x^22 + 30*x^21 + 60*x^20 + 99*x^19 + 88*x^18 + 11*x^17 + 50*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 18*x^8 + 118*x^7 + 24*x^6 + 110*x^5 + 60*x^4 + 5*x^3 + 56*x^2 + 77*x + 46, x^27 + 33*x^25 + 62*x^24 + 38*x^23 + 24*x^22 + 126*x^21 + 60*x^20 + 67*x^19 + 56*x^18 + 43*x^17 + 34*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 98*x^8 + 22*x^7 + 56*x^6 + 78*x^5 + 60*x^4 + 101*x^3 + 24*x^2 + 109*x + 126, x^27 + 33*x^25 + 22*x^24 + 38*x^23 + 8*x^22 + 30*x^21 + 92*x^20 + 3*x^19 + 72*x^18 + 75*x^17 + 26*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 42*x^8 + 22*x^7 + 104*x^6 + 110*x^5 + 28*x^4 + 37*x^3 + 104*x^2 + 13*x + 102, x^27 + 33*x^25 + 54*x^24 + 54*x^23 + 120*x^22 + 46*x^21 + 76*x^20 + 115*x^19 + 88*x^18 + 59*x^17 + 74*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 42*x^8 + 102*x^7 + 24*x^6 + 62*x^5 + 76*x^4 + 85*x^3 + 56*x^2 + 61*x + 22, x^27 + 33*x^25 + 14*x^24 + 102*x^23 + 24*x^22 + 62*x^21 + 28*x^20 + 3*x^19 + 56*x^18 + 107*x^17 + 18*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 18*x^8 + 86*x^7 + 56*x^6 + 14*x^5 + 28*x^4 + 37*x^3 + 24*x^2 + 45*x + 14, x^27 + 33*x^25 + 106*x^24 + 118*x^23 + 8*x^22 + 46*x^21 + 52*x^20 + 51*x^19 + 40*x^18 + 59*x^17 + 86*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 54*x^8 + 38*x^7 + 104*x^6 + 62*x^5 + 52*x^4 + 21*x^3 + 72*x^2 + 61*x + 74, x^27 + 33*x^25 + 26*x^24 + 54*x^23 + 104*x^22 + 46*x^21 + 116*x^20 + 115*x^19 + 72*x^18 + 59*x^17 + 70*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 70*x^8 + 102*x^7 + 72*x^6 + 62*x^5 + 116*x^4 + 85*x^3 + 104*x^2 + 61*x + 26, x^27 + 33*x^25 + 102*x^24 + 86*x^23 + 24*x^22 + 14*x^21 + 76*x^20 + 83*x^19 + 56*x^18 + 91*x^17 + 122*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 58*x^8 + 6*x^7 + 56*x^6 + 30*x^5 + 76*x^4 + 53*x^3 + 24*x^2 + 93*x + 38, x^27 + 33*x^25 + 14*x^24 + 6*x^23 + 56*x^22 + 94*x^21 + 60*x^20 + 99*x^19 + 24*x^18 + 75*x^17 + 114*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 82*x^8 + 118*x^7 + 88*x^6 + 46*x^5 + 60*x^4 + 5*x^3 + 120*x^2 + 13*x + 110, x^27 + 33*x^25 + 94*x^24 + 38*x^23 + 24*x^22 + 126*x^21 + 124*x^20 + 67*x^19 + 56*x^18 + 43*x^17 + 2*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 66*x^8 + 22*x^7 + 56*x^6 + 78*x^5 + 124*x^4 + 101*x^3 + 24*x^2 + 109*x + 30, x^27 + 33*x^25 + 74*x^24 + 86*x^23 + 40*x^22 + 78*x^21 + 84*x^20 + 83*x^19 + 8*x^18 + 27*x^17 + 22*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 22*x^8 + 6*x^7 + 8*x^6 + 94*x^5 + 84*x^4 + 53*x^3 + 40*x^2 + 29*x + 74, x^27 + 33*x^25 + 10*x^24 + 102*x^23 + 24*x^22 + 94*x^21 + 4*x^20 + 67*x^19 + 24*x^18 + 11*x^17 + 38*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 118*x^8 + 86*x^7 + 56*x^6 + 46*x^5 + 68*x^4 + 101*x^3 + 120*x^2 + 77*x + 26, x^27 + 33*x^25 + 118*x^24 + 22*x^23 + 24*x^22 + 14*x^21 + 108*x^20 + 19*x^19 + 56*x^18 + 91*x^17 + 106*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 42*x^8 + 70*x^7 + 56*x^6 + 30*x^5 + 108*x^4 + 117*x^3 + 24*x^2 + 93*x + 54, x^27 + 33*x^25 + 94*x^24 + 6*x^23 + 56*x^22 + 30*x^21 + 92*x^20 + 99*x^19 + 24*x^18 + 11*x^17 + 34*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 2*x^8 + 118*x^7 + 88*x^6 + 110*x^5 + 92*x^4 + 5*x^3 + 120*x^2 + 77*x + 62, x^27 + 33*x^25 + 94*x^24 + 102*x^23 + 24*x^22 + 62*x^21 + 124*x^20 + 3*x^19 + 56*x^18 + 107*x^17 + 2*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 66*x^8 + 86*x^7 + 56*x^6 + 14*x^5 + 124*x^4 + 37*x^3 + 24*x^2 + 45*x + 30, x^27 + 33*x^25 + 82*x^24 + 70*x^23 + 40*x^22 + 94*x^21 + 36*x^20 + 35*x^19 + 8*x^18 + 75*x^17 + 14*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 14*x^8 + 54*x^7 + 8*x^6 + 46*x^5 + 36*x^4 + 69*x^3 + 40*x^2 + 13*x + 82, x^27 + 33*x^25 + 30*x^24 + 86*x^23 + 72*x^22 + 110*x^21 + 44*x^20 + 19*x^19 + 8*x^18 + 59*x^17 + 18*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 34*x^8 + 6*x^7 + 40*x^6 + 126*x^5 + 108*x^4 + 117*x^3 + 40*x^2 + 61*x + 110, x^27 + 33*x^25 + 38*x^24 + 6*x^23 + 8*x^22 + 62*x^21 + 124*x^20 + 35*x^19 + 72*x^18 + 43*x^17 + 10*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 26*x^8 + 118*x^7 + 104*x^6 + 14*x^5 + 60*x^4 + 69*x^3 + 104*x^2 + 109*x + 118, x^27 + 33*x^25 + 106*x^24 + 70*x^23 + 24*x^22 + 126*x^21 + 4*x^20 + 99*x^19 + 24*x^18 + 107*x^17 + 6*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 22*x^8 + 54*x^7 + 56*x^6 + 78*x^5 + 68*x^4 + 5*x^3 + 120*x^2 + 45*x + 58, x^27 + 33*x^25 + 86*x^24 + 102*x^23 + 72*x^22 + 30*x^21 + 92*x^20 + 67*x^19 + 8*x^18 + 75*x^17 + 90*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 106*x^8 + 86*x^7 + 40*x^6 + 110*x^5 + 28*x^4 + 101*x^3 + 40*x^2 + 13*x + 38, x^27 + 33*x^25 + 6*x^24 + 22*x^23 + 56*x^22 + 14*x^21 + 108*x^20 + 19*x^19 + 24*x^18 + 91*x^17 + 122*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 90*x^8 + 70*x^7 + 88*x^6 + 30*x^5 + 108*x^4 + 117*x^3 + 120*x^2 + 93*x + 102, x^27 + 33*x^25 + 122*x^24 + 38*x^23 + 56*x^22 + 94*x^21 + 4*x^20 + 3*x^19 + 120*x^18 + 11*x^17 + 22*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 70*x^8 + 22*x^7 + 88*x^6 + 46*x^5 + 68*x^4 + 37*x^3 + 88*x^2 + 77*x + 106, x^27 + 33*x^25 + 90*x^24 + 86*x^23 + 72*x^22 + 14*x^21 + 20*x^20 + 83*x^19 + 104*x^18 + 91*x^17 + 102*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 70*x^8 + 6*x^7 + 40*x^6 + 30*x^5 + 20*x^4 + 53*x^3 + 8*x^2 + 93*x + 58, x^27 + 33*x^25 + 98*x^24 + 22*x^23 + 88*x^22 + 110*x^21 + 52*x^20 + 83*x^19 + 88*x^18 + 59*x^17 + 14*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 30*x^8 + 70*x^7 + 120*x^6 + 126*x^5 + 116*x^4 + 53*x^3 + 56*x^2 + 61*x + 50, x^27 + 33*x^25 + 62*x^24 + 102*x^23 + 24*x^22 + 126*x^21 + 124*x^20 + 3*x^19 + 56*x^18 + 43*x^17 + 98*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 98*x^8 + 86*x^7 + 56*x^6 + 78*x^5 + 124*x^4 + 37*x^3 + 24*x^2 + 109*x + 62, x^27 + 33*x^25 + 94*x^24 + 6*x^23 + 88*x^22 + 94*x^21 + 60*x^20 + 99*x^19 + 120*x^18 + 75*x^17 + 66*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 66*x^8 + 118*x^7 + 120*x^6 + 46*x^5 + 60*x^4 + 5*x^3 + 88*x^2 + 13*x + 94, x^27 + 33*x^25 + 110*x^24 + 86*x^23 + 8*x^22 + 46*x^21 + 12*x^20 + 19*x^19 + 72*x^18 + 123*x^17 + 2*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 82*x^8 + 6*x^7 + 104*x^6 + 62*x^5 + 76*x^4 + 117*x^3 + 104*x^2 + 125*x + 126, x^27 + 33*x^25 + 102*x^24 + 102*x^23 + 8*x^22 + 30*x^21 + 124*x^20 + 67*x^19 + 72*x^18 + 75*x^17 + 74*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 90*x^8 + 86*x^7 + 104*x^6 + 110*x^5 + 60*x^4 + 101*x^3 + 104*x^2 + 13*x + 54, x^27 + 33*x^25 + 66*x^24 + 86*x^23 + 56*x^22 + 46*x^21 + 84*x^20 + 19*x^19 + 120*x^18 + 123*x^17 + 78*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 126*x^8 + 6*x^7 + 88*x^6 + 62*x^5 + 20*x^4 + 117*x^3 + 88*x^2 + 125*x + 50, x^27 + 33*x^25 + 114*x^24 + 86*x^23 + 56*x^22 + 110*x^21 + 52*x^20 + 19*x^19 + 120*x^18 + 59*x^17 + 30*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 78*x^8 + 6*x^7 + 88*x^6 + 126*x^5 + 116*x^4 + 117*x^3 + 88*x^2 + 61*x + 98, x^27 + 33*x^25 + 62*x^24 + 38*x^23 + 120*x^22 + 62*x^21 + 92*x^20 + 67*x^19 + 88*x^18 + 107*x^17 + 2*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 34*x^8 + 22*x^7 + 24*x^6 + 14*x^5 + 92*x^4 + 101*x^3 + 56*x^2 + 45*x + 94, x^27 + 33*x^25 + 126*x^24 + 118*x^23 + 8*x^22 + 14*x^21 + 44*x^20 + 115*x^19 + 72*x^18 + 27*x^17 + 114*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 66*x^8 + 38*x^7 + 104*x^6 + 30*x^5 + 108*x^4 + 85*x^3 + 104*x^2 + 29*x + 14, x^27 + 33*x^25 + 46*x^24 + 6*x^23 + 88*x^22 + 94*x^21 + 28*x^20 + 99*x^19 + 120*x^18 + 75*x^17 + 50*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 114*x^8 + 118*x^7 + 120*x^6 + 46*x^5 + 28*x^4 + 5*x^3 + 88*x^2 + 13*x + 110, x^27 + 33*x^25 + 46*x^24 + 22*x^23 + 8*x^22 + 46*x^21 + 76*x^20 + 83*x^19 + 72*x^18 + 123*x^17 + 2*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 18*x^8 + 70*x^7 + 104*x^6 + 62*x^5 + 12*x^4 + 53*x^3 + 104*x^2 + 125*x + 126, x^27 + 33*x^25 + 10*x^24 + 6*x^23 + 120*x^22 + 126*x^21 + 100*x^20 + 35*x^19 + 56*x^18 + 107*x^17 + 70*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 54*x^8 + 118*x^7 + 24*x^6 + 78*x^5 + 36*x^4 + 69*x^3 + 24*x^2 + 45*x + 58, x^27 + 33*x^25 + 114*x^24 + 118*x^23 + 24*x^22 + 14*x^21 + 20*x^20 + 115*x^19 + 24*x^18 + 27*x^17 + 62*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 14*x^8 + 38*x^7 + 56*x^6 + 30*x^5 + 84*x^4 + 85*x^3 + 120*x^2 + 29*x + 2, x^27 + 33*x^25 + 106*x^24 + 70*x^23 + 88*x^22 + 126*x^21 + 68*x^20 + 99*x^19 + 88*x^18 + 107*x^17 + 70*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 22*x^8 + 54*x^7 + 120*x^6 + 78*x^5 + 4*x^4 + 5*x^3 + 56*x^2 + 45*x + 122, x^27 + 33*x^25 + 58*x^24 + 38*x^23 + 88*x^22 + 30*x^21 + 100*x^20 + 3*x^19 + 88*x^18 + 75*x^17 + 118*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 70*x^8 + 22*x^7 + 120*x^6 + 110*x^5 + 36*x^4 + 37*x^3 + 56*x^2 + 13*x + 74, x^27 + 33*x^25 + 58*x^24 + 70*x^23 + 120*x^22 + 62*x^21 + 4*x^20 + 99*x^19 + 56*x^18 + 43*x^17 + 86*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 6*x^8 + 54*x^7 + 24*x^6 + 14*x^5 + 68*x^4 + 5*x^3 + 24*x^2 + 109*x + 42, x^27 + 33*x^25 + 18*x^24 + 86*x^23 + 24*x^22 + 110*x^21 + 84*x^20 + 19*x^19 + 24*x^18 + 59*x^17 + 30*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 110*x^8 + 6*x^7 + 56*x^6 + 126*x^5 + 20*x^4 + 117*x^3 + 120*x^2 + 61*x + 34, x^27 + 33*x^25 + 34*x^24 + 70*x^23 + 72*x^22 + 94*x^21 + 36*x^20 + 35*x^19 + 104*x^18 + 75*x^17 + 94*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 126*x^8 + 54*x^7 + 40*x^6 + 46*x^5 + 36*x^4 + 69*x^3 + 8*x^2 + 13*x + 66, x^27 + 33*x^25 + 2*x^24 + 6*x^23 + 72*x^22 + 94*x^21 + 36*x^20 + 99*x^19 + 104*x^18 + 75*x^17 + 62*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 30*x^8 + 118*x^7 + 40*x^6 + 46*x^5 + 36*x^4 + 5*x^3 + 8*x^2 + 13*x + 98, x^27 + 33*x^25 + 78*x^24 + 54*x^23 + 40*x^22 + 14*x^21 + 108*x^20 + 51*x^19 + 40*x^18 + 27*x^17 + 2*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 50*x^8 + 102*x^7 + 8*x^6 + 30*x^5 + 44*x^4 + 21*x^3 + 72*x^2 + 29*x + 62, x^27 + 33*x^25 + 98*x^24 + 6*x^23 + 40*x^22 + 30*x^21 + 4*x^20 + 99*x^19 + 8*x^18 + 11*x^17 + 62*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 126*x^8 + 118*x^7 + 8*x^6 + 110*x^5 + 4*x^4 + 5*x^3 + 40*x^2 + 77*x + 34, x^27 + 33*x^25 + 106*x^24 + 6*x^23 + 88*x^22 + 62*x^21 + 68*x^20 + 35*x^19 + 88*x^18 + 43*x^17 + 70*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 22*x^8 + 118*x^7 + 120*x^6 + 14*x^5 + 4*x^4 + 69*x^3 + 56*x^2 + 109*x + 122, x^27 + 33*x^25 + 82*x^24 + 22*x^23 + 56*x^22 + 46*x^21 + 116*x^20 + 83*x^19 + 120*x^18 + 123*x^17 + 62*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 110*x^8 + 70*x^7 + 88*x^6 + 62*x^5 + 52*x^4 + 53*x^3 + 88*x^2 + 125*x + 66, x^27 + 33*x^25 + 10*x^24 + 86*x^23 + 72*x^22 + 78*x^21 + 116*x^20 + 83*x^19 + 104*x^18 + 27*x^17 + 54*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 22*x^8 + 6*x^7 + 40*x^6 + 94*x^5 + 116*x^4 + 53*x^3 + 8*x^2 + 29*x + 106, x^27 + 33*x^25 + 58*x^24 + 38*x^23 + 24*x^22 + 94*x^21 + 100*x^20 + 3*x^19 + 24*x^18 + 11*x^17 + 118*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 70*x^8 + 22*x^7 + 56*x^6 + 46*x^5 + 36*x^4 + 37*x^3 + 120*x^2 + 77*x + 74, x^27 + 33*x^25 + 22*x^24 + 86*x^23 + 56*x^22 + 14*x^21 + 12*x^20 + 83*x^19 + 24*x^18 + 91*x^17 + 106*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 74*x^8 + 6*x^7 + 88*x^6 + 30*x^5 + 12*x^4 + 53*x^3 + 120*x^2 + 93*x + 118, x^27 + 33*x^25 + 18*x^24 + 38*x^23 + 72*x^22 + 62*x^21 + 68*x^20 + 67*x^19 + 104*x^18 + 107*x^17 + 46*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 14*x^8 + 22*x^7 + 40*x^6 + 14*x^5 + 68*x^4 + 101*x^3 + 8*x^2 + 45*x + 114, x^27 + 33*x^25 + 26*x^24 + 70*x^23 + 88*x^22 + 62*x^21 + 36*x^20 + 99*x^19 + 88*x^18 + 43*x^17 + 22*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 102*x^8 + 54*x^7 + 120*x^6 + 14*x^5 + 100*x^4 + 5*x^3 + 56*x^2 + 109*x + 42, x^27 + 33*x^25 + 66*x^24 + 38*x^23 + 104*x^22 + 126*x^21 + 68*x^20 + 67*x^19 + 72*x^18 + 43*x^17 + 94*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 30*x^8 + 22*x^7 + 72*x^6 + 78*x^5 + 68*x^4 + 101*x^3 + 104*x^2 + 109*x + 2, x^27 + 33*x^25 + 110*x^24 + 38*x^23 + 24*x^22 + 62*x^21 + 28*x^20 + 67*x^19 + 56*x^18 + 107*x^17 + 114*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 50*x^8 + 22*x^7 + 56*x^6 + 14*x^5 + 28*x^4 + 101*x^3 + 24*x^2 + 45*x + 46, x^27 + 33*x^25 + 14*x^24 + 102*x^23 + 120*x^22 + 126*x^21 + 60*x^20 + 3*x^19 + 88*x^18 + 43*x^17 + 114*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 82*x^8 + 86*x^7 + 24*x^6 + 78*x^5 + 60*x^4 + 37*x^3 + 56*x^2 + 109*x + 110, x^27 + 33*x^25 + 2*x^24 + 86*x^23 + 88*x^22 + 110*x^21 + 52*x^20 + 19*x^19 + 88*x^18 + 59*x^17 + 46*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 126*x^8 + 6*x^7 + 120*x^6 + 126*x^5 + 116*x^4 + 117*x^3 + 56*x^2 + 61*x + 18, x^27 + 33*x^25 + 114*x^24 + 38*x^23 + 72*x^22 + 62*x^21 + 4*x^20 + 67*x^19 + 104*x^18 + 107*x^17 + 78*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 46*x^8 + 22*x^7 + 40*x^6 + 14*x^5 + 4*x^4 + 101*x^3 + 8*x^2 + 45*x + 82, x^27 + 33*x^25 + 118*x^24 + 54*x^23 + 88*x^22 + 110*x^21 + 108*x^20 + 115*x^19 + 120*x^18 + 123*x^17 + 106*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 42*x^8 + 102*x^7 + 120*x^6 + 126*x^5 + 108*x^4 + 85*x^3 + 88*x^2 + 125*x + 54, x^27 + 33*x^25 + 2*x^24 + 102*x^23 + 8*x^22 + 126*x^21 + 36*x^20 + 3*x^19 + 40*x^18 + 43*x^17 + 62*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 30*x^8 + 86*x^7 + 104*x^6 + 78*x^5 + 36*x^4 + 37*x^3 + 72*x^2 + 109*x + 98, x^27 + 33*x^25 + 74*x^24 + 102*x^23 + 24*x^22 + 30*x^21 + 68*x^20 + 67*x^19 + 24*x^18 + 75*x^17 + 38*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 54*x^8 + 86*x^7 + 56*x^6 + 110*x^5 + 4*x^4 + 101*x^3 + 120*x^2 + 13*x + 26, x^27 + 33*x^25 + 70*x^24 + 6*x^23 + 8*x^22 + 62*x^21 + 60*x^20 + 35*x^19 + 72*x^18 + 43*x^17 + 106*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 122*x^8 + 118*x^7 + 104*x^6 + 14*x^5 + 124*x^4 + 69*x^3 + 104*x^2 + 109*x + 22, x^27 + 33*x^25 + 30*x^24 + 102*x^23 + 120*x^22 + 126*x^21 + 28*x^20 + 3*x^19 + 88*x^18 + 43*x^17 + 34*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 66*x^8 + 86*x^7 + 24*x^6 + 78*x^5 + 28*x^4 + 37*x^3 + 56*x^2 + 109*x + 62, x^27 + 33*x^25 + 126*x^24 + 38*x^23 + 56*x^22 + 62*x^21 + 28*x^20 + 67*x^19 + 24*x^18 + 107*x^17 + 2*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 98*x^8 + 22*x^7 + 88*x^6 + 14*x^5 + 28*x^4 + 101*x^3 + 120*x^2 + 45*x + 94, x^27 + 33*x^25 + 42*x^24 + 102*x^23 + 56*x^22 + 30*x^21 + 36*x^20 + 67*x^19 + 120*x^18 + 75*x^17 + 38*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 22*x^8 + 86*x^7 + 88*x^6 + 110*x^5 + 100*x^4 + 101*x^3 + 88*x^2 + 13*x + 90, x^27 + 33*x^25 + 2*x^24 + 86*x^23 + 24*x^22 + 110*x^21 + 116*x^20 + 19*x^19 + 24*x^18 + 59*x^17 + 110*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 126*x^8 + 6*x^7 + 56*x^6 + 126*x^5 + 52*x^4 + 117*x^3 + 120*x^2 + 61*x + 82, x^27 + 33*x^25 + 118*x^24 + 54*x^23 + 120*x^22 + 110*x^21 + 12*x^20 + 115*x^19 + 88*x^18 + 123*x^17 + 74*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 106*x^8 + 102*x^7 + 24*x^6 + 126*x^5 + 12*x^4 + 85*x^3 + 56*x^2 + 125*x + 22, x^27 + 33*x^25 + 2*x^24 + 118*x^23 + 56*x^22 + 78*x^21 + 84*x^20 + 115*x^19 + 120*x^18 + 91*x^17 + 14*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 62*x^8 + 38*x^7 + 88*x^6 + 94*x^5 + 20*x^4 + 85*x^3 + 88*x^2 + 93*x + 114, x^27 + 33*x^25 + 30*x^24 + 118*x^23 + 104*x^22 + 78*x^21 + 12*x^20 + 115*x^19 + 104*x^18 + 91*x^17 + 50*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 98*x^8 + 38*x^7 + 72*x^6 + 94*x^5 + 76*x^4 + 85*x^3 + 8*x^2 + 93*x + 14, x^27 + 33*x^25 + 26*x^24 + 102*x^23 + 24*x^22 + 30*x^21 + 36*x^20 + 67*x^19 + 24*x^18 + 75*x^17 + 22*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 102*x^8 + 86*x^7 + 56*x^6 + 110*x^5 + 100*x^4 + 101*x^3 + 120*x^2 + 13*x + 42, x^27 + 33*x^25 + 98*x^24 + 6*x^23 + 8*x^22 + 30*x^21 + 100*x^20 + 99*x^19 + 40*x^18 + 11*x^17 + 94*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 62*x^8 + 118*x^7 + 104*x^6 + 110*x^5 + 100*x^4 + 5*x^3 + 72*x^2 + 77*x + 66, x^27 + 33*x^25 + 46*x^24 + 54*x^23 + 8*x^22 + 14*x^21 + 12*x^20 + 51*x^19 + 72*x^18 + 27*x^17 + 66*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 18*x^8 + 102*x^7 + 104*x^6 + 30*x^5 + 76*x^4 + 21*x^3 + 104*x^2 + 29*x + 62, x^27 + 33*x^25 + 102*x^24 + 118*x^23 + 56*x^22 + 46*x^21 + 108*x^20 + 51*x^19 + 24*x^18 + 59*x^17 + 90*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 122*x^8 + 38*x^7 + 88*x^6 + 62*x^5 + 108*x^4 + 21*x^3 + 120*x^2 + 61*x + 6, x^27 + 33*x^25 + 38*x^24 + 70*x^23 + 8*x^22 + 126*x^21 + 124*x^20 + 99*x^19 + 72*x^18 + 107*x^17 + 10*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 26*x^8 + 54*x^7 + 104*x^6 + 78*x^5 + 60*x^4 + 5*x^3 + 104*x^2 + 45*x + 118, x^27 + 33*x^25 + 90*x^24 + 118*x^23 + 104*x^22 + 110*x^21 + 116*x^20 + 51*x^19 + 72*x^18 + 123*x^17 + 6*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 6*x^8 + 38*x^7 + 72*x^6 + 126*x^5 + 116*x^4 + 21*x^3 + 104*x^2 + 125*x + 90, x^27 + 33*x^25 + 34*x^24 + 38*x^23 + 40*x^22 + 126*x^21 + 68*x^20 + 67*x^19 + 8*x^18 + 43*x^17 + 62*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 62*x^8 + 22*x^7 + 8*x^6 + 78*x^5 + 68*x^4 + 101*x^3 + 40*x^2 + 109*x + 34, x^27 + 33*x^25 + 10*x^24 + 86*x^23 + 40*x^22 + 78*x^21 + 84*x^20 + 83*x^19 + 8*x^18 + 27*x^17 + 86*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 86*x^8 + 6*x^7 + 8*x^6 + 94*x^5 + 84*x^4 + 53*x^3 + 40*x^2 + 29*x + 10, x^27 + 33*x^25 + 10*x^24 + 54*x^23 + 8*x^22 + 110*x^21 + 116*x^20 + 115*x^19 + 40*x^18 + 123*x^17 + 54*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 22*x^8 + 102*x^7 + 104*x^6 + 126*x^5 + 116*x^4 + 85*x^3 + 72*x^2 + 125*x + 106, x^27 + 33*x^25 + 70*x^24 + 102*x^23 + 72*x^22 + 30*x^21 + 124*x^20 + 67*x^19 + 8*x^18 + 75*x^17 + 42*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 122*x^8 + 86*x^7 + 40*x^6 + 110*x^5 + 60*x^4 + 101*x^3 + 40*x^2 + 13*x + 86, x^27 + 33*x^25 + 14*x^24 + 86*x^23 + 8*x^22 + 46*x^21 + 76*x^20 + 19*x^19 + 72*x^18 + 123*x^17 + 98*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 50*x^8 + 6*x^7 + 104*x^6 + 62*x^5 + 12*x^4 + 117*x^3 + 104*x^2 + 125*x + 30, x^27 + 33*x^25 + 2*x^24 + 86*x^23 + 88*x^22 + 46*x^21 + 116*x^20 + 19*x^19 + 88*x^18 + 123*x^17 + 110*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 126*x^8 + 6*x^7 + 120*x^6 + 62*x^5 + 52*x^4 + 117*x^3 + 56*x^2 + 125*x + 82, x^27 + 33*x^25 + 34*x^24 + 102*x^23 + 40*x^22 + 62*x^21 + 68*x^20 + 3*x^19 + 8*x^18 + 107*x^17 + 62*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 62*x^8 + 86*x^7 + 8*x^6 + 14*x^5 + 68*x^4 + 37*x^3 + 40*x^2 + 45*x + 34, x^27 + 33*x^25 + 114*x^24 + 38*x^23 + 40*x^22 + 126*x^21 + 36*x^20 + 67*x^19 + 8*x^18 + 43*x^17 + 46*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 110*x^8 + 22*x^7 + 8*x^6 + 78*x^5 + 36*x^4 + 101*x^3 + 40*x^2 + 109*x + 50, x^27 + 33*x^25 + 22*x^24 + 118*x^23 + 120*x^22 + 46*x^21 + 76*x^20 + 51*x^19 + 88*x^18 + 59*x^17 + 42*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 74*x^8 + 38*x^7 + 24*x^6 + 62*x^5 + 76*x^4 + 21*x^3 + 56*x^2 + 61*x + 54, x^27 + 33*x^25 + 6*x^24 + 22*x^23 + 56*x^22 + 78*x^21 + 44*x^20 + 19*x^19 + 24*x^18 + 27*x^17 + 58*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 90*x^8 + 70*x^7 + 88*x^6 + 94*x^5 + 44*x^4 + 117*x^3 + 120*x^2 + 29*x + 38, x^27 + 33*x^25 + 94*x^24 + 118*x^23 + 8*x^22 + 14*x^21 + 108*x^20 + 115*x^19 + 72*x^18 + 27*x^17 + 18*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 98*x^8 + 38*x^7 + 104*x^6 + 30*x^5 + 44*x^4 + 85*x^3 + 104*x^2 + 29*x + 110, x^27 + 33*x^25 + 114*x^24 + 102*x^23 + 40*x^22 + 62*x^21 + 36*x^20 + 3*x^19 + 8*x^18 + 107*x^17 + 46*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 110*x^8 + 86*x^7 + 8*x^6 + 14*x^5 + 36*x^4 + 37*x^3 + 40*x^2 + 45*x + 50, x^27 + 33*x^25 + 110*x^24 + 102*x^23 + 56*x^22 + 62*x^21 + 124*x^20 + 3*x^19 + 24*x^18 + 107*x^17 + 18*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 114*x^8 + 86*x^7 + 88*x^6 + 14*x^5 + 124*x^4 + 37*x^3 + 120*x^2 + 45*x + 78, x^27 + 33*x^25 + 50*x^24 + 6*x^23 + 104*x^22 + 30*x^21 + 36*x^20 + 99*x^19 + 72*x^18 + 11*x^17 + 110*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 46*x^8 + 118*x^7 + 72*x^6 + 110*x^5 + 36*x^4 + 5*x^3 + 104*x^2 + 77*x + 114, x^27 + 33*x^25 + 18*x^24 + 118*x^23 + 56*x^22 + 78*x^21 + 52*x^20 + 115*x^19 + 120*x^18 + 91*x^17 + 62*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 46*x^8 + 38*x^7 + 88*x^6 + 94*x^5 + 116*x^4 + 85*x^3 + 88*x^2 + 93*x + 66, x^27 + 33*x^25 + 30*x^24 + 6*x^23 + 120*x^22 + 94*x^21 + 92*x^20 + 99*x^19 + 88*x^18 + 75*x^17 + 98*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 66*x^8 + 118*x^7 + 24*x^6 + 46*x^5 + 92*x^4 + 5*x^3 + 56*x^2 + 13*x + 126, x^27 + 33*x^25 + 66*x^24 + 118*x^23 + 120*x^22 + 14*x^21 + 84*x^20 + 115*x^19 + 56*x^18 + 27*x^17 + 78*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 126*x^8 + 38*x^7 + 24*x^6 + 30*x^5 + 20*x^4 + 85*x^3 + 24*x^2 + 29*x + 50, x^27 + 33*x^25 + 38*x^24 + 38*x^23 + 72*x^22 + 30*x^21 + 124*x^20 + 3*x^19 + 8*x^18 + 75*x^17 + 10*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 26*x^8 + 22*x^7 + 40*x^6 + 110*x^5 + 60*x^4 + 37*x^3 + 40*x^2 + 13*x + 118, x^27 + 33*x^25 + 70*x^24 + 22*x^23 + 120*x^22 + 14*x^21 + 44*x^20 + 19*x^19 + 88*x^18 + 91*x^17 + 122*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 26*x^8 + 70*x^7 + 24*x^6 + 30*x^5 + 44*x^4 + 117*x^3 + 56*x^2 + 93*x + 102, x^27 + 33*x^25 + 30*x^24 + 38*x^23 + 120*x^22 + 126*x^21 + 92*x^20 + 67*x^19 + 88*x^18 + 43*x^17 + 98*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 66*x^8 + 22*x^7 + 24*x^6 + 78*x^5 + 92*x^4 + 101*x^3 + 56*x^2 + 109*x + 126, x^27 + 33*x^25 + 26*x^24 + 102*x^23 + 56*x^22 + 94*x^21 + 4*x^20 + 67*x^19 + 120*x^18 + 11*x^17 + 54*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 38*x^8 + 86*x^7 + 88*x^6 + 46*x^5 + 68*x^4 + 101*x^3 + 88*x^2 + 77*x + 74, x^27 + 33*x^25 + 126*x^24 + 6*x^23 + 120*x^22 + 30*x^21 + 92*x^20 + 99*x^19 + 88*x^18 + 11*x^17 + 66*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 98*x^8 + 118*x^7 + 24*x^6 + 110*x^5 + 92*x^4 + 5*x^3 + 56*x^2 + 77*x + 30, x^27 + 33*x^25 + 86*x^24 + 22*x^23 + 56*x^22 + 78*x^21 + 12*x^20 + 19*x^19 + 24*x^18 + 27*x^17 + 42*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 10*x^8 + 70*x^7 + 88*x^6 + 94*x^5 + 12*x^4 + 117*x^3 + 120*x^2 + 29*x + 54, x^27 + 33*x^25 + 50*x^24 + 54*x^23 + 24*x^22 + 78*x^21 + 20*x^20 + 51*x^19 + 24*x^18 + 91*x^17 + 126*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 78*x^8 + 102*x^7 + 56*x^6 + 94*x^5 + 84*x^4 + 21*x^3 + 120*x^2 + 93*x + 66, x^27 + 33*x^25 + 114*x^24 + 54*x^23 + 120*x^22 + 14*x^21 + 52*x^20 + 51*x^19 + 56*x^18 + 27*x^17 + 30*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 78*x^8 + 102*x^7 + 24*x^6 + 30*x^5 + 116*x^4 + 21*x^3 + 24*x^2 + 29*x + 98, x^27 + 33*x^25 + 18*x^24 + 38*x^23 + 8*x^22 + 126*x^21 + 68*x^20 + 67*x^19 + 40*x^18 + 43*x^17 + 46*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 14*x^8 + 22*x^7 + 104*x^6 + 78*x^5 + 68*x^4 + 101*x^3 + 72*x^2 + 109*x + 114, x^27 + 33*x^25 + 126*x^24 + 118*x^23 + 40*x^22 + 78*x^21 + 12*x^20 + 115*x^19 + 40*x^18 + 91*x^17 + 18*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 2*x^8 + 38*x^7 + 8*x^6 + 94*x^5 + 76*x^4 + 85*x^3 + 72*x^2 + 93*x + 46, x^27 + 33*x^25 + 90*x^24 + 70*x^23 + 24*x^22 + 62*x^21 + 100*x^20 + 99*x^19 + 24*x^18 + 43*x^17 + 22*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 38*x^8 + 54*x^7 + 56*x^6 + 14*x^5 + 36*x^4 + 5*x^3 + 120*x^2 + 109*x + 42, x^27 + 33*x^25 + 126*x^24 + 118*x^23 + 104*x^22 + 14*x^21 + 12*x^20 + 115*x^19 + 104*x^18 + 27*x^17 + 18*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 2*x^8 + 38*x^7 + 72*x^6 + 30*x^5 + 76*x^4 + 85*x^3 + 8*x^2 + 29*x + 46, x^27 + 33*x^25 + 126*x^24 + 22*x^23 + 8*x^22 + 46*x^21 + 44*x^20 + 83*x^19 + 72*x^18 + 123*x^17 + 114*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 66*x^8 + 70*x^7 + 104*x^6 + 62*x^5 + 108*x^4 + 53*x^3 + 104*x^2 + 125*x + 14, x^27 + 33*x^25 + 38*x^24 + 54*x^23 + 24*x^22 + 110*x^21 + 76*x^20 + 115*x^19 + 56*x^18 + 123*x^17 + 58*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 122*x^8 + 102*x^7 + 56*x^6 + 126*x^5 + 76*x^4 + 85*x^3 + 24*x^2 + 125*x + 102, x^27 + 33*x^25 + 22*x^24 + 102*x^23 + 8*x^22 + 94*x^21 + 92*x^20 + 67*x^19 + 72*x^18 + 11*x^17 + 26*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 42*x^8 + 86*x^7 + 104*x^6 + 46*x^5 + 28*x^4 + 101*x^3 + 104*x^2 + 77*x + 102, x^27 + 33*x^25 + 6*x^24 + 22*x^23 + 24*x^22 + 78*x^21 + 12*x^20 + 19*x^19 + 56*x^18 + 27*x^17 + 90*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 26*x^8 + 70*x^7 + 56*x^6 + 94*x^5 + 12*x^4 + 117*x^3 + 24*x^2 + 29*x + 70, x^27 + 33*x^25 + 14*x^24 + 70*x^23 + 56*x^22 + 94*x^21 + 124*x^20 + 35*x^19 + 24*x^18 + 75*x^17 + 50*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 82*x^8 + 54*x^7 + 88*x^6 + 46*x^5 + 124*x^4 + 69*x^3 + 120*x^2 + 13*x + 46, x^27 + 33*x^25 + 110*x^24 + 22*x^23 + 8*x^22 + 46*x^21 + 76*x^20 + 83*x^19 + 72*x^18 + 123*x^17 + 66*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 82*x^8 + 70*x^7 + 104*x^6 + 62*x^5 + 12*x^4 + 53*x^3 + 104*x^2 + 125*x + 62, x^27 + 33*x^25 + 62*x^24 + 102*x^23 + 120*x^22 + 126*x^21 + 92*x^20 + 3*x^19 + 88*x^18 + 43*x^17 + 2*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 34*x^8 + 86*x^7 + 24*x^6 + 78*x^5 + 92*x^4 + 37*x^3 + 56*x^2 + 109*x + 94, x^27 + 33*x^25 + 86*x^24 + 70*x^23 + 8*x^22 + 62*x^21 + 92*x^20 + 99*x^19 + 72*x^18 + 43*x^17 + 90*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 106*x^8 + 54*x^7 + 104*x^6 + 14*x^5 + 28*x^4 + 5*x^3 + 104*x^2 + 109*x + 38, x^27 + 33*x^25 + 110*x^24 + 6*x^23 + 120*x^22 + 30*x^21 + 124*x^20 + 99*x^19 + 88*x^18 + 11*x^17 + 18*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 114*x^8 + 118*x^7 + 24*x^6 + 110*x^5 + 124*x^4 + 5*x^3 + 56*x^2 + 77*x + 78, x^27 + 33*x^25 + 94*x^24 + 54*x^23 + 40*x^22 + 14*x^21 + 76*x^20 + 51*x^19 + 40*x^18 + 27*x^17 + 50*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 34*x^8 + 102*x^7 + 8*x^6 + 30*x^5 + 12*x^4 + 21*x^3 + 72*x^2 + 29*x + 14, x^27 + 33*x^25 + 82*x^24 + 6*x^23 + 104*x^22 + 94*x^21 + 36*x^20 + 99*x^19 + 72*x^18 + 75*x^17 + 14*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 14*x^8 + 118*x^7 + 72*x^6 + 46*x^5 + 36*x^4 + 5*x^3 + 104*x^2 + 13*x + 82, x^27 + 33*x^25 + 110*x^24 + 102*x^23 + 120*x^22 + 126*x^21 + 124*x^20 + 3*x^19 + 88*x^18 + 43*x^17 + 18*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 114*x^8 + 86*x^7 + 24*x^6 + 78*x^5 + 124*x^4 + 37*x^3 + 56*x^2 + 109*x + 78, x^27 + 33*x^25 + 2*x^24 + 54*x^23 + 24*x^22 + 14*x^21 + 52*x^20 + 51*x^19 + 24*x^18 + 27*x^17 + 46*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 126*x^8 + 102*x^7 + 56*x^6 + 30*x^5 + 116*x^4 + 21*x^3 + 120*x^2 + 29*x + 18, x^27 + 33*x^25 + 26*x^24 + 118*x^23 + 72*x^22 + 46*x^21 + 20*x^20 + 51*x^19 + 104*x^18 + 59*x^17 + 38*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 6*x^8 + 38*x^7 + 40*x^6 + 62*x^5 + 20*x^4 + 21*x^3 + 8*x^2 + 61*x + 122, x^27 + 33*x^25 + 62*x^24 + 6*x^23 + 88*x^22 + 30*x^21 + 60*x^20 + 99*x^19 + 120*x^18 + 11*x^17 + 34*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 98*x^8 + 118*x^7 + 120*x^6 + 110*x^5 + 60*x^4 + 5*x^3 + 88*x^2 + 77*x + 126, x^27 + 33*x^25 + 46*x^24 + 6*x^23 + 24*x^22 + 30*x^21 + 28*x^20 + 99*x^19 + 56*x^18 + 11*x^17 + 50*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 114*x^8 + 118*x^7 + 56*x^6 + 110*x^5 + 28*x^4 + 5*x^3 + 24*x^2 + 77*x + 110, x^27 + 33*x^25 + 22*x^24 + 6*x^23 + 8*x^22 + 62*x^21 + 28*x^20 + 35*x^19 + 72*x^18 + 43*x^17 + 90*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 42*x^8 + 118*x^7 + 104*x^6 + 14*x^5 + 92*x^4 + 69*x^3 + 104*x^2 + 109*x + 38, x^27 + 33*x^25 + 118*x^24 + 22*x^23 + 56*x^22 + 78*x^21 + 76*x^20 + 19*x^19 + 24*x^18 + 27*x^17 + 10*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 106*x^8 + 70*x^7 + 88*x^6 + 94*x^5 + 76*x^4 + 117*x^3 + 120*x^2 + 29*x + 86, x^27 + 33*x^25 + 82*x^24 + 118*x^23 + 88*x^22 + 14*x^21 + 20*x^20 + 115*x^19 + 88*x^18 + 27*x^17 + 30*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 46*x^8 + 38*x^7 + 120*x^6 + 30*x^5 + 84*x^4 + 85*x^3 + 56*x^2 + 29*x + 34, x^27 + 33*x^25 + 6*x^24 + 70*x^23 + 8*x^22 + 126*x^21 + 60*x^20 + 99*x^19 + 72*x^18 + 107*x^17 + 42*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 58*x^8 + 54*x^7 + 104*x^6 + 78*x^5 + 124*x^4 + 5*x^3 + 104*x^2 + 45*x + 86, x^27 + 33*x^25 + 58*x^24 + 6*x^23 + 120*x^22 + 62*x^21 + 68*x^20 + 35*x^19 + 56*x^18 + 43*x^17 + 22*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 6*x^8 + 118*x^7 + 24*x^6 + 14*x^5 + 4*x^4 + 69*x^3 + 24*x^2 + 109*x + 106, x^27 + 33*x^25 + 38*x^24 + 6*x^23 + 40*x^22 + 126*x^21 + 92*x^20 + 35*x^19 + 40*x^18 + 107*x^17 + 42*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 90*x^8 + 118*x^7 + 8*x^6 + 78*x^5 + 28*x^4 + 69*x^3 + 72*x^2 + 45*x + 22, x^27 + 33*x^25 + 82*x^24 + 38*x^23 + 104*x^22 + 62*x^21 + 100*x^20 + 67*x^19 + 72*x^18 + 107*x^17 + 78*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 14*x^8 + 22*x^7 + 72*x^6 + 14*x^5 + 100*x^4 + 101*x^3 + 104*x^2 + 45*x + 18, x^27 + 33*x^25 + 102*x^24 + 118*x^23 + 24*x^22 + 46*x^21 + 76*x^20 + 51*x^19 + 56*x^18 + 59*x^17 + 122*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 58*x^8 + 38*x^7 + 56*x^6 + 62*x^5 + 76*x^4 + 21*x^3 + 24*x^2 + 61*x + 38, x^27 + 33*x^25 + 42*x^24 + 102*x^23 + 120*x^22 + 30*x^21 + 100*x^20 + 67*x^19 + 56*x^18 + 75*x^17 + 102*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 22*x^8 + 86*x^7 + 24*x^6 + 110*x^5 + 36*x^4 + 101*x^3 + 24*x^2 + 13*x + 26, x^27 + 33*x^25 + 58*x^24 + 70*x^23 + 24*x^22 + 126*x^21 + 100*x^20 + 99*x^19 + 24*x^18 + 107*x^17 + 118*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 70*x^8 + 54*x^7 + 56*x^6 + 78*x^5 + 36*x^4 + 5*x^3 + 120*x^2 + 45*x + 74, x^27 + 33*x^25 + 42*x^24 + 70*x^23 + 56*x^22 + 126*x^21 + 36*x^20 + 99*x^19 + 120*x^18 + 107*x^17 + 38*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 22*x^8 + 54*x^7 + 88*x^6 + 78*x^5 + 100*x^4 + 5*x^3 + 88*x^2 + 45*x + 90, x^27 + 33*x^25 + 58*x^24 + 86*x^23 + 104*x^22 + 78*x^21 + 52*x^20 + 83*x^19 + 72*x^18 + 27*x^17 + 38*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 38*x^8 + 6*x^7 + 72*x^6 + 94*x^5 + 52*x^4 + 53*x^3 + 104*x^2 + 29*x + 58, x^27 + 33*x^25 + 126*x^24 + 22*x^23 + 104*x^22 + 110*x^21 + 76*x^20 + 83*x^19 + 104*x^18 + 59*x^17 + 82*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 2*x^8 + 70*x^7 + 72*x^6 + 126*x^5 + 12*x^4 + 53*x^3 + 8*x^2 + 61*x + 110, x^27 + 33*x^25 + 122*x^24 + 118*x^23 + 40*x^22 + 46*x^21 + 52*x^20 + 51*x^19 + 8*x^18 + 59*x^17 + 102*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 102*x^8 + 38*x^7 + 8*x^6 + 62*x^5 + 52*x^4 + 21*x^3 + 40*x^2 + 61*x + 122, x^27 + 33*x^25 + 2*x^24 + 102*x^23 + 72*x^22 + 62*x^21 + 36*x^20 + 3*x^19 + 104*x^18 + 107*x^17 + 62*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 30*x^8 + 86*x^7 + 40*x^6 + 14*x^5 + 36*x^4 + 37*x^3 + 8*x^2 + 45*x + 98, x^27 + 33*x^25 + 58*x^24 + 54*x^23 + 104*x^22 + 110*x^21 + 116*x^20 + 115*x^19 + 72*x^18 + 123*x^17 + 102*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 38*x^8 + 102*x^7 + 72*x^6 + 126*x^5 + 116*x^4 + 85*x^3 + 104*x^2 + 125*x + 122, x^27 + 33*x^25 + 18*x^24 + 70*x^23 + 8*x^22 + 94*x^21 + 4*x^20 + 35*x^19 + 40*x^18 + 75*x^17 + 110*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 14*x^8 + 54*x^7 + 104*x^6 + 46*x^5 + 4*x^4 + 69*x^3 + 72*x^2 + 13*x + 50, x^27 + 33*x^25 + 46*x^24 + 118*x^23 + 8*x^22 + 78*x^21 + 12*x^20 + 115*x^19 + 72*x^18 + 91*x^17 + 66*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 18*x^8 + 38*x^7 + 104*x^6 + 94*x^5 + 76*x^4 + 85*x^3 + 104*x^2 + 93*x + 62, x^27 + 33*x^25 + 82*x^24 + 70*x^23 + 72*x^22 + 30*x^21 + 4*x^20 + 35*x^19 + 104*x^18 + 11*x^17 + 46*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 78*x^8 + 54*x^7 + 40*x^6 + 110*x^5 + 4*x^4 + 69*x^3 + 8*x^2 + 77*x + 114, x^27 + 33*x^25 + 30*x^24 + 38*x^23 + 120*x^22 + 62*x^21 + 28*x^20 + 67*x^19 + 88*x^18 + 107*x^17 + 34*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 66*x^8 + 22*x^7 + 24*x^6 + 14*x^5 + 28*x^4 + 101*x^3 + 56*x^2 + 45*x + 62, x^27 + 33*x^25 + 70*x^24 + 86*x^23 + 88*x^22 + 14*x^21 + 76*x^20 + 83*x^19 + 120*x^18 + 91*x^17 + 90*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 90*x^8 + 6*x^7 + 120*x^6 + 30*x^5 + 76*x^4 + 53*x^3 + 88*x^2 + 93*x + 70, x^27 + 33*x^25 + 2*x^24 + 54*x^23 + 88*x^22 + 14*x^21 + 116*x^20 + 51*x^19 + 88*x^18 + 27*x^17 + 110*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 126*x^8 + 102*x^7 + 120*x^6 + 30*x^5 + 52*x^4 + 21*x^3 + 56*x^2 + 29*x + 82, x^27 + 33*x^25 + 34*x^24 + 6*x^23 + 40*x^22 + 30*x^21 + 4*x^20 + 99*x^19 + 8*x^18 + 11*x^17 + 126*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 62*x^8 + 118*x^7 + 8*x^6 + 110*x^5 + 4*x^4 + 5*x^3 + 40*x^2 + 77*x + 98, x^27 + 33*x^25 + 90*x^24 + 70*x^23 + 24*x^22 + 126*x^21 + 36*x^20 + 99*x^19 + 24*x^18 + 107*x^17 + 86*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 38*x^8 + 54*x^7 + 56*x^6 + 78*x^5 + 100*x^4 + 5*x^3 + 120*x^2 + 45*x + 106, x^27 + 33*x^25 + 86*x^24 + 54*x^23 + 56*x^22 + 110*x^21 + 12*x^20 + 115*x^19 + 24*x^18 + 123*x^17 + 42*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 10*x^8 + 102*x^7 + 88*x^6 + 126*x^5 + 12*x^4 + 85*x^3 + 120*x^2 + 125*x + 54, x^27 + 33*x^25 + 18*x^24 + 118*x^23 + 24*x^22 + 78*x^21 + 20*x^20 + 115*x^19 + 24*x^18 + 91*x^17 + 94*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 110*x^8 + 38*x^7 + 56*x^6 + 94*x^5 + 84*x^4 + 85*x^3 + 120*x^2 + 93*x + 98, x^27 + 33*x^25 + 50*x^24 + 86*x^23 + 24*x^22 + 110*x^21 + 20*x^20 + 19*x^19 + 24*x^18 + 59*x^17 + 126*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 78*x^8 + 6*x^7 + 56*x^6 + 126*x^5 + 84*x^4 + 117*x^3 + 120*x^2 + 61*x + 66, x^27 + 33*x^25 + 70*x^24 + 22*x^23 + 24*x^22 + 78*x^21 + 12*x^20 + 19*x^19 + 56*x^18 + 27*x^17 + 26*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 90*x^8 + 70*x^7 + 56*x^6 + 94*x^5 + 12*x^4 + 117*x^3 + 24*x^2 + 29*x + 6, x^27 + 33*x^25 + 62*x^24 + 6*x^23 + 24*x^22 + 30*x^21 + 124*x^20 + 99*x^19 + 56*x^18 + 11*x^17 + 98*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 98*x^8 + 118*x^7 + 56*x^6 + 110*x^5 + 124*x^4 + 5*x^3 + 24*x^2 + 77*x + 62, x^27 + 33*x^25 + 74*x^24 + 38*x^23 + 120*x^22 + 94*x^21 + 36*x^20 + 3*x^19 + 56*x^18 + 11*x^17 + 70*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 118*x^8 + 22*x^7 + 24*x^6 + 46*x^5 + 100*x^4 + 37*x^3 + 24*x^2 + 77*x + 58, x^27 + 33*x^25 + 126*x^24 + 86*x^23 + 40*x^22 + 46*x^21 + 12*x^20 + 19*x^19 + 40*x^18 + 123*x^17 + 18*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 2*x^8 + 6*x^7 + 8*x^6 + 62*x^5 + 76*x^4 + 117*x^3 + 72*x^2 + 125*x + 46, x^27 + 33*x^25 + 18*x^24 + 118*x^23 + 88*x^22 + 14*x^21 + 20*x^20 + 115*x^19 + 88*x^18 + 27*x^17 + 94*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 110*x^8 + 38*x^7 + 120*x^6 + 30*x^5 + 84*x^4 + 85*x^3 + 56*x^2 + 29*x + 98, x^27 + 33*x^25 + 122*x^24 + 70*x^23 + 24*x^22 + 62*x^21 + 36*x^20 + 99*x^19 + 24*x^18 + 43*x^17 + 118*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 6*x^8 + 54*x^7 + 56*x^6 + 14*x^5 + 100*x^4 + 5*x^3 + 120*x^2 + 109*x + 74, x^27 + 33*x^25 + 54*x^24 + 118*x^23 + 88*x^22 + 110*x^21 + 44*x^20 + 51*x^19 + 120*x^18 + 123*x^17 + 106*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 106*x^8 + 38*x^7 + 120*x^6 + 126*x^5 + 44*x^4 + 21*x^3 + 88*x^2 + 125*x + 54, x^27 + 33*x^25 + 6*x^24 + 102*x^23 + 8*x^22 + 94*x^21 + 124*x^20 + 67*x^19 + 72*x^18 + 11*x^17 + 106*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 58*x^8 + 86*x^7 + 104*x^6 + 46*x^5 + 60*x^4 + 101*x^3 + 104*x^2 + 77*x + 22, x^27 + 33*x^25 + 110*x^24 + 6*x^23 + 88*x^22 + 30*x^21 + 92*x^20 + 99*x^19 + 120*x^18 + 11*x^17 + 50*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 50*x^8 + 118*x^7 + 120*x^6 + 110*x^5 + 92*x^4 + 5*x^3 + 88*x^2 + 77*x + 110, x^27 + 33*x^25 + 98*x^24 + 54*x^23 + 56*x^22 + 78*x^21 + 84*x^20 + 51*x^19 + 120*x^18 + 91*x^17 + 110*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 94*x^8 + 102*x^7 + 88*x^6 + 94*x^5 + 20*x^4 + 21*x^3 + 88*x^2 + 93*x + 18, x^27 + 33*x^25 + 42*x^24 + 70*x^23 + 24*x^22 + 126*x^21 + 4*x^20 + 99*x^19 + 24*x^18 + 107*x^17 + 70*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 86*x^8 + 54*x^7 + 56*x^6 + 78*x^5 + 68*x^4 + 5*x^3 + 120*x^2 + 45*x + 122, x^27 + 33*x^25 + 86*x^24 + 118*x^23 + 88*x^22 + 110*x^21 + 108*x^20 + 51*x^19 + 120*x^18 + 123*x^17 + 74*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 74*x^8 + 38*x^7 + 120*x^6 + 126*x^5 + 108*x^4 + 21*x^3 + 88*x^2 + 125*x + 86, x^27 + 33*x^25 + 118*x^24 + 102*x^23 + 104*x^22 + 94*x^21 + 124*x^20 + 67*x^19 + 104*x^18 + 11*x^17 + 90*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 10*x^8 + 86*x^7 + 72*x^6 + 46*x^5 + 60*x^4 + 101*x^3 + 8*x^2 + 77*x + 102, x^27 + 33*x^25 + 114*x^24 + 102*x^23 + 40*x^22 + 126*x^21 + 100*x^20 + 3*x^19 + 8*x^18 + 43*x^17 + 110*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 110*x^8 + 86*x^7 + 8*x^6 + 78*x^5 + 100*x^4 + 37*x^3 + 40*x^2 + 109*x + 114, x^27 + 33*x^25 + 34*x^24 + 38*x^23 + 40*x^22 + 62*x^21 + 4*x^20 + 67*x^19 + 8*x^18 + 107*x^17 + 126*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 62*x^8 + 22*x^7 + 8*x^6 + 14*x^5 + 4*x^4 + 101*x^3 + 40*x^2 + 45*x + 98, x^27 + 33*x^25 + 54*x^24 + 38*x^23 + 72*x^22 + 94*x^21 + 28*x^20 + 3*x^19 + 8*x^18 + 11*x^17 + 122*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 10*x^8 + 22*x^7 + 40*x^6 + 46*x^5 + 92*x^4 + 37*x^3 + 40*x^2 + 77*x + 6, x^27 + 33*x^25 + 30*x^24 + 118*x^23 + 72*x^22 + 78*x^21 + 108*x^20 + 115*x^19 + 8*x^18 + 91*x^17 + 82*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 34*x^8 + 38*x^7 + 40*x^6 + 94*x^5 + 44*x^4 + 85*x^3 + 40*x^2 + 93*x + 46, x^27 + 33*x^25 + 6*x^24 + 54*x^23 + 24*x^22 + 46*x^21 + 76*x^20 + 115*x^19 + 56*x^18 + 59*x^17 + 26*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 26*x^8 + 102*x^7 + 56*x^6 + 62*x^5 + 76*x^4 + 85*x^3 + 24*x^2 + 61*x + 6, x^27 + 33*x^25 + 74*x^24 + 6*x^23 + 88*x^22 + 62*x^21 + 4*x^20 + 35*x^19 + 88*x^18 + 43*x^17 + 102*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 54*x^8 + 118*x^7 + 120*x^6 + 14*x^5 + 68*x^4 + 69*x^3 + 56*x^2 + 109*x + 90, x^27 + 33*x^25 + 38*x^24 + 38*x^23 + 40*x^22 + 94*x^21 + 28*x^20 + 3*x^19 + 40*x^18 + 11*x^17 + 106*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 90*x^8 + 22*x^7 + 8*x^6 + 46*x^5 + 92*x^4 + 37*x^3 + 72*x^2 + 77*x + 86, x^27 + 33*x^25 + 30*x^24 + 118*x^23 + 8*x^22 + 14*x^21 + 108*x^20 + 115*x^19 + 72*x^18 + 27*x^17 + 82*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 34*x^8 + 38*x^7 + 104*x^6 + 30*x^5 + 44*x^4 + 85*x^3 + 104*x^2 + 29*x + 46, x^27 + 33*x^25 + 122*x^24 + 54*x^23 + 72*x^22 + 110*x^21 + 84*x^20 + 115*x^19 + 104*x^18 + 123*x^17 + 70*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 38*x^8 + 102*x^7 + 40*x^6 + 126*x^5 + 84*x^4 + 85*x^3 + 8*x^2 + 125*x + 90, x^27 + 33*x^25 + 50*x^24 + 70*x^23 + 104*x^22 + 94*x^21 + 36*x^20 + 35*x^19 + 72*x^18 + 75*x^17 + 110*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 46*x^8 + 54*x^7 + 72*x^6 + 46*x^5 + 36*x^4 + 69*x^3 + 104*x^2 + 13*x + 114, x^27 + 33*x^25 + 114*x^24 + 70*x^23 + 104*x^22 + 30*x^21 + 100*x^20 + 35*x^19 + 72*x^18 + 11*x^17 + 110*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 110*x^8 + 54*x^7 + 72*x^6 + 110*x^5 + 100*x^4 + 69*x^3 + 104*x^2 + 77*x + 114, x^27 + 33*x^25 + 2*x^24 + 70*x^23 + 40*x^22 + 94*x^21 + 68*x^20 + 35*x^19 + 8*x^18 + 75*x^17 + 30*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 94*x^8 + 54*x^7 + 8*x^6 + 46*x^5 + 68*x^4 + 69*x^3 + 40*x^2 + 13*x + 66, x^27 + 33*x^25 + 18*x^24 + 38*x^23 + 104*x^22 + 62*x^21 + 100*x^20 + 67*x^19 + 72*x^18 + 107*x^17 + 14*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 78*x^8 + 22*x^7 + 72*x^6 + 14*x^5 + 100*x^4 + 101*x^3 + 104*x^2 + 45*x + 82, x^27 + 33*x^25 + 122*x^24 + 22*x^23 + 72*x^22 + 78*x^21 + 84*x^20 + 19*x^19 + 104*x^18 + 27*x^17 + 70*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 38*x^8 + 70*x^7 + 40*x^6 + 94*x^5 + 84*x^4 + 117*x^3 + 8*x^2 + 29*x + 90, x^27 + 33*x^25 + 2*x^24 + 118*x^23 + 120*x^22 + 14*x^21 + 84*x^20 + 115*x^19 + 56*x^18 + 27*x^17 + 14*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 62*x^8 + 38*x^7 + 24*x^6 + 30*x^5 + 20*x^4 + 85*x^3 + 24*x^2 + 29*x + 114, x^27 + 33*x^25 + 82*x^24 + 54*x^23 + 120*x^22 + 78*x^21 + 52*x^20 + 51*x^19 + 56*x^18 + 91*x^17 + 126*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 110*x^8 + 102*x^7 + 24*x^6 + 94*x^5 + 116*x^4 + 21*x^3 + 24*x^2 + 93*x + 2, x^27 + 33*x^25 + 54*x^24 + 6*x^23 + 104*x^22 + 126*x^21 + 124*x^20 + 35*x^19 + 104*x^18 + 107*x^17 + 26*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 74*x^8 + 118*x^7 + 72*x^6 + 78*x^5 + 60*x^4 + 69*x^3 + 8*x^2 + 45*x + 38, x^27 + 33*x^25 + 102*x^24 + 22*x^23 + 120*x^22 + 14*x^21 + 108*x^20 + 19*x^19 + 88*x^18 + 91*x^17 + 90*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 122*x^8 + 70*x^7 + 24*x^6 + 30*x^5 + 108*x^4 + 117*x^3 + 56*x^2 + 93*x + 6, x^27 + 33*x^25 + 26*x^24 + 70*x^23 + 24*x^22 + 62*x^21 + 100*x^20 + 99*x^19 + 24*x^18 + 43*x^17 + 86*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 102*x^8 + 54*x^7 + 56*x^6 + 14*x^5 + 36*x^4 + 5*x^3 + 120*x^2 + 109*x + 106, x^27 + 33*x^25 + 42*x^24 + 54*x^23 + 8*x^22 + 110*x^21 + 52*x^20 + 115*x^19 + 40*x^18 + 123*x^17 + 22*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 118*x^8 + 102*x^7 + 104*x^6 + 126*x^5 + 52*x^4 + 85*x^3 + 72*x^2 + 125*x + 10, x^27 + 33*x^25 + 22*x^24 + 22*x^23 + 88*x^22 + 14*x^21 + 108*x^20 + 19*x^19 + 120*x^18 + 91*x^17 + 10*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 10*x^8 + 70*x^7 + 120*x^6 + 30*x^5 + 108*x^4 + 117*x^3 + 88*x^2 + 93*x + 22, x^27 + 33*x^25 + 70*x^24 + 54*x^23 + 24*x^22 + 46*x^21 + 76*x^20 + 115*x^19 + 56*x^18 + 59*x^17 + 90*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 90*x^8 + 102*x^7 + 56*x^6 + 62*x^5 + 76*x^4 + 85*x^3 + 24*x^2 + 61*x + 70, x^27 + 33*x^25 + 110*x^24 + 22*x^23 + 72*x^22 + 110*x^21 + 76*x^20 + 83*x^19 + 8*x^18 + 59*x^17 + 66*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 82*x^8 + 70*x^7 + 40*x^6 + 126*x^5 + 12*x^4 + 53*x^3 + 40*x^2 + 61*x + 62, x^27 + 33*x^25 + 114*x^24 + 54*x^23 + 24*x^22 + 78*x^21 + 20*x^20 + 51*x^19 + 24*x^18 + 91*x^17 + 62*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 14*x^8 + 102*x^7 + 56*x^6 + 94*x^5 + 84*x^4 + 21*x^3 + 120*x^2 + 93*x + 2, x^27 + 33*x^25 + 58*x^24 + 102*x^23 + 120*x^22 + 94*x^21 + 4*x^20 + 67*x^19 + 56*x^18 + 11*x^17 + 86*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 6*x^8 + 86*x^7 + 24*x^6 + 46*x^5 + 68*x^4 + 101*x^3 + 24*x^2 + 77*x + 42, x^27 + 33*x^25 + 10*x^24 + 54*x^23 + 72*x^22 + 46*x^21 + 116*x^20 + 115*x^19 + 104*x^18 + 59*x^17 + 54*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 22*x^8 + 102*x^7 + 40*x^6 + 62*x^5 + 116*x^4 + 85*x^3 + 8*x^2 + 61*x + 106, x^27 + 33*x^25 + 30*x^24 + 102*x^23 + 120*x^22 + 62*x^21 + 92*x^20 + 3*x^19 + 88*x^18 + 107*x^17 + 98*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 66*x^8 + 86*x^7 + 24*x^6 + 14*x^5 + 92*x^4 + 37*x^3 + 56*x^2 + 45*x + 126, x^27 + 33*x^25 + 46*x^24 + 70*x^23 + 120*x^22 + 30*x^21 + 60*x^20 + 35*x^19 + 88*x^18 + 11*x^17 + 18*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 50*x^8 + 54*x^7 + 24*x^6 + 110*x^5 + 60*x^4 + 69*x^3 + 56*x^2 + 77*x + 78, x^27 + 33*x^25 + 70*x^24 + 22*x^23 + 120*x^22 + 78*x^21 + 108*x^20 + 19*x^19 + 88*x^18 + 27*x^17 + 58*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 26*x^8 + 70*x^7 + 24*x^6 + 94*x^5 + 108*x^4 + 117*x^3 + 56*x^2 + 29*x + 38, x^27 + 33*x^25 + 102*x^24 + 6*x^23 + 104*x^22 + 126*x^21 + 28*x^20 + 35*x^19 + 104*x^18 + 107*x^17 + 42*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 26*x^8 + 118*x^7 + 72*x^6 + 78*x^5 + 92*x^4 + 69*x^3 + 8*x^2 + 45*x + 22, x^27 + 33*x^25 + 34*x^24 + 86*x^23 + 120*x^22 + 110*x^21 + 20*x^20 + 19*x^19 + 56*x^18 + 59*x^17 + 110*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 30*x^8 + 6*x^7 + 24*x^6 + 126*x^5 + 84*x^4 + 117*x^3 + 24*x^2 + 61*x + 18, x^27 + 33*x^25 + 6*x^24 + 54*x^23 + 24*x^22 + 110*x^21 + 12*x^20 + 115*x^19 + 56*x^18 + 123*x^17 + 90*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 26*x^8 + 102*x^7 + 56*x^6 + 126*x^5 + 12*x^4 + 85*x^3 + 24*x^2 + 125*x + 70, x^27 + 33*x^25 + 50*x^24 + 70*x^23 + 8*x^22 + 30*x^21 + 4*x^20 + 35*x^19 + 40*x^18 + 11*x^17 + 14*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 110*x^8 + 54*x^7 + 104*x^6 + 110*x^5 + 4*x^4 + 69*x^3 + 72*x^2 + 77*x + 18, x^27 + 33*x^25 + 90*x^24 + 6*x^23 + 56*x^22 + 62*x^21 + 68*x^20 + 35*x^19 + 120*x^18 + 43*x^17 + 54*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 102*x^8 + 118*x^7 + 88*x^6 + 14*x^5 + 4*x^4 + 69*x^3 + 88*x^2 + 109*x + 74, x^27 + 33*x^25 + 2*x^24 + 38*x^23 + 40*x^22 + 126*x^21 + 4*x^20 + 67*x^19 + 8*x^18 + 43*x^17 + 94*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 94*x^8 + 22*x^7 + 8*x^6 + 78*x^5 + 4*x^4 + 101*x^3 + 40*x^2 + 109*x + 2, x^27 + 33*x^25 + 94*x^24 + 54*x^23 + 8*x^22 + 78*x^21 + 108*x^20 + 51*x^19 + 72*x^18 + 91*x^17 + 18*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 98*x^8 + 102*x^7 + 104*x^6 + 94*x^5 + 44*x^4 + 21*x^3 + 104*x^2 + 93*x + 110, x^27 + 33*x^25 + 74*x^24 + 70*x^23 + 56*x^22 + 62*x^21 + 36*x^20 + 99*x^19 + 120*x^18 + 43*x^17 + 70*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 118*x^8 + 54*x^7 + 88*x^6 + 14*x^5 + 100*x^4 + 5*x^3 + 88*x^2 + 109*x + 58, x^27 + 33*x^25 + 82*x^24 + 102*x^23 + 104*x^22 + 62*x^21 + 36*x^20 + 3*x^19 + 72*x^18 + 107*x^17 + 14*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 14*x^8 + 86*x^7 + 72*x^6 + 14*x^5 + 36*x^4 + 37*x^3 + 104*x^2 + 45*x + 82, x^27 + 33*x^25 + 34*x^24 + 6*x^23 + 104*x^22 + 30*x^21 + 68*x^20 + 99*x^19 + 72*x^18 + 11*x^17 + 62*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 62*x^8 + 118*x^7 + 72*x^6 + 110*x^5 + 68*x^4 + 5*x^3 + 104*x^2 + 77*x + 34, x^27 + 33*x^25 + 2*x^24 + 102*x^23 + 40*x^22 + 62*x^21 + 4*x^20 + 3*x^19 + 8*x^18 + 107*x^17 + 94*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 94*x^8 + 86*x^7 + 8*x^6 + 14*x^5 + 4*x^4 + 37*x^3 + 40*x^2 + 45*x + 2, x^27 + 33*x^25 + 38*x^24 + 22*x^23 + 24*x^22 + 78*x^21 + 76*x^20 + 19*x^19 + 56*x^18 + 27*x^17 + 58*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 122*x^8 + 70*x^7 + 56*x^6 + 94*x^5 + 76*x^4 + 117*x^3 + 24*x^2 + 29*x + 102, x^27 + 33*x^25 + 22*x^24 + 118*x^23 + 88*x^22 + 110*x^21 + 108*x^20 + 51*x^19 + 120*x^18 + 123*x^17 + 10*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 10*x^8 + 38*x^7 + 120*x^6 + 126*x^5 + 108*x^4 + 21*x^3 + 88*x^2 + 125*x + 22, x^27 + 33*x^25 + 94*x^24 + 118*x^23 + 40*x^22 + 14*x^21 + 12*x^20 + 115*x^19 + 40*x^18 + 27*x^17 + 114*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 34*x^8 + 38*x^7 + 8*x^6 + 30*x^5 + 76*x^4 + 85*x^3 + 72*x^2 + 29*x + 78, x^27 + 33*x^25 + 114*x^24 + 6*x^23 + 104*x^22 + 30*x^21 + 36*x^20 + 99*x^19 + 72*x^18 + 11*x^17 + 46*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 110*x^8 + 118*x^7 + 72*x^6 + 110*x^5 + 36*x^4 + 5*x^3 + 104*x^2 + 77*x + 50, x^27 + 33*x^25 + 70*x^24 + 6*x^23 + 8*x^22 + 126*x^21 + 124*x^20 + 35*x^19 + 72*x^18 + 107*x^17 + 42*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 122*x^8 + 118*x^7 + 104*x^6 + 78*x^5 + 60*x^4 + 69*x^3 + 104*x^2 + 45*x + 86, x^27 + 33*x^25 + 58*x^24 + 38*x^23 + 88*x^22 + 94*x^21 + 36*x^20 + 3*x^19 + 88*x^18 + 11*x^17 + 54*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 70*x^8 + 22*x^7 + 120*x^6 + 46*x^5 + 100*x^4 + 37*x^3 + 56*x^2 + 77*x + 10, x^27 + 33*x^25 + 86*x^24 + 6*x^23 + 40*x^22 + 126*x^21 + 124*x^20 + 35*x^19 + 40*x^18 + 107*x^17 + 58*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 42*x^8 + 118*x^7 + 8*x^6 + 78*x^5 + 60*x^4 + 69*x^3 + 72*x^2 + 45*x + 6, x^27 + 33*x^25 + 30*x^24 + 70*x^23 + 56*x^22 + 94*x^21 + 92*x^20 + 35*x^19 + 24*x^18 + 75*x^17 + 98*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 66*x^8 + 54*x^7 + 88*x^6 + 46*x^5 + 92*x^4 + 69*x^3 + 120*x^2 + 13*x + 126, x^27 + 33*x^25 + 86*x^24 + 6*x^23 + 8*x^22 + 62*x^21 + 28*x^20 + 35*x^19 + 72*x^18 + 43*x^17 + 26*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 106*x^8 + 118*x^7 + 104*x^6 + 14*x^5 + 92*x^4 + 69*x^3 + 104*x^2 + 109*x + 102, x^27 + 33*x^25 + 74*x^24 + 6*x^23 + 120*x^22 + 62*x^21 + 36*x^20 + 35*x^19 + 56*x^18 + 43*x^17 + 70*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 118*x^8 + 118*x^7 + 24*x^6 + 14*x^5 + 100*x^4 + 69*x^3 + 24*x^2 + 109*x + 58, x^27 + 33*x^25 + 42*x^24 + 54*x^23 + 40*x^22 + 110*x^21 + 84*x^20 + 115*x^19 + 8*x^18 + 123*x^17 + 118*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 54*x^8 + 102*x^7 + 8*x^6 + 126*x^5 + 84*x^4 + 85*x^3 + 40*x^2 + 125*x + 106, x^27 + 33*x^25 + 114*x^24 + 54*x^23 + 88*x^22 + 78*x^21 + 84*x^20 + 51*x^19 + 88*x^18 + 91*x^17 + 126*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 14*x^8 + 102*x^7 + 120*x^6 + 94*x^5 + 20*x^4 + 21*x^3 + 56*x^2 + 93*x + 66, x^27 + 33*x^25 + 14*x^24 + 22*x^23 + 72*x^22 + 110*x^21 + 12*x^20 + 83*x^19 + 8*x^18 + 59*x^17 + 34*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 50*x^8 + 70*x^7 + 40*x^6 + 126*x^5 + 76*x^4 + 53*x^3 + 40*x^2 + 61*x + 94, x^27 + 33*x^25 + 98*x^24 + 86*x^23 + 56*x^22 + 110*x^21 + 84*x^20 + 19*x^19 + 120*x^18 + 59*x^17 + 110*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 94*x^8 + 6*x^7 + 88*x^6 + 126*x^5 + 20*x^4 + 117*x^3 + 88*x^2 + 61*x + 18, x^27 + 33*x^25 + 114*x^24 + 70*x^23 + 104*x^22 + 94*x^21 + 36*x^20 + 35*x^19 + 72*x^18 + 75*x^17 + 46*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 110*x^8 + 54*x^7 + 72*x^6 + 46*x^5 + 36*x^4 + 69*x^3 + 104*x^2 + 13*x + 50, x^27 + 33*x^25 + 10*x^24 + 70*x^23 + 24*x^22 + 62*x^21 + 4*x^20 + 99*x^19 + 24*x^18 + 43*x^17 + 38*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 118*x^8 + 54*x^7 + 56*x^6 + 14*x^5 + 68*x^4 + 5*x^3 + 120*x^2 + 109*x + 26, x^27 + 33*x^25 + 22*x^24 + 102*x^23 + 72*x^22 + 30*x^21 + 92*x^20 + 67*x^19 + 8*x^18 + 75*x^17 + 26*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 42*x^8 + 86*x^7 + 40*x^6 + 110*x^5 + 28*x^4 + 101*x^3 + 40*x^2 + 13*x + 102, x^27 + 33*x^25 + 110*x^24 + 118*x^23 + 40*x^22 + 14*x^21 + 108*x^20 + 115*x^19 + 40*x^18 + 27*x^17 + 34*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 18*x^8 + 38*x^7 + 8*x^6 + 30*x^5 + 44*x^4 + 85*x^3 + 72*x^2 + 29*x + 30, x^27 + 33*x^25 + 74*x^24 + 54*x^23 + 8*x^22 + 46*x^21 + 52*x^20 + 115*x^19 + 40*x^18 + 59*x^17 + 54*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 86*x^8 + 102*x^7 + 104*x^6 + 62*x^5 + 52*x^4 + 85*x^3 + 72*x^2 + 61*x + 106, x^27 + 33*x^25 + 42*x^24 + 22*x^23 + 40*x^22 + 78*x^21 + 84*x^20 + 19*x^19 + 8*x^18 + 27*x^17 + 118*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 54*x^8 + 70*x^7 + 8*x^6 + 94*x^5 + 84*x^4 + 117*x^3 + 40*x^2 + 29*x + 106, x^27 + 33*x^25 + 82*x^24 + 70*x^23 + 8*x^22 + 30*x^21 + 68*x^20 + 35*x^19 + 40*x^18 + 11*x^17 + 110*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 78*x^8 + 54*x^7 + 104*x^6 + 110*x^5 + 68*x^4 + 69*x^3 + 72*x^2 + 77*x + 50, x^27 + 33*x^25 + 46*x^24 + 86*x^23 + 8*x^22 + 46*x^21 + 12*x^20 + 19*x^19 + 72*x^18 + 123*x^17 + 66*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 18*x^8 + 6*x^7 + 104*x^6 + 62*x^5 + 76*x^4 + 117*x^3 + 104*x^2 + 125*x + 62, x^27 + 33*x^25 + 2*x^24 + 102*x^23 + 104*x^22 + 62*x^21 + 68*x^20 + 3*x^19 + 72*x^18 + 107*x^17 + 30*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 94*x^8 + 86*x^7 + 72*x^6 + 14*x^5 + 68*x^4 + 37*x^3 + 104*x^2 + 45*x + 66, x^27 + 33*x^25 + 30*x^24 + 86*x^23 + 72*x^22 + 46*x^21 + 108*x^20 + 19*x^19 + 8*x^18 + 123*x^17 + 82*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 34*x^8 + 6*x^7 + 40*x^6 + 62*x^5 + 44*x^4 + 117*x^3 + 40*x^2 + 125*x + 46, x^27 + 33*x^25 + 106*x^24 + 38*x^23 + 88*x^22 + 94*x^21 + 68*x^20 + 3*x^19 + 88*x^18 + 11*x^17 + 70*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 22*x^8 + 22*x^7 + 120*x^6 + 46*x^5 + 4*x^4 + 37*x^3 + 56*x^2 + 77*x + 122, x^27 + 33*x^25 + 98*x^24 + 102*x^23 + 72*x^22 + 126*x^21 + 36*x^20 + 3*x^19 + 104*x^18 + 43*x^17 + 30*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 62*x^8 + 86*x^7 + 40*x^6 + 78*x^5 + 36*x^4 + 37*x^3 + 8*x^2 + 109*x + 2, x^27 + 33*x^25 + 102*x^24 + 22*x^23 + 88*x^22 + 14*x^21 + 76*x^20 + 19*x^19 + 120*x^18 + 91*x^17 + 122*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 58*x^8 + 70*x^7 + 120*x^6 + 30*x^5 + 76*x^4 + 117*x^3 + 88*x^2 + 93*x + 38, x^27 + 33*x^25 + 110*x^24 + 54*x^23 + 72*x^22 + 14*x^21 + 76*x^20 + 51*x^19 + 8*x^18 + 27*x^17 + 66*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 82*x^8 + 102*x^7 + 40*x^6 + 30*x^5 + 12*x^4 + 21*x^3 + 40*x^2 + 29*x + 62, x^27 + 33*x^25 + 78*x^24 + 38*x^23 + 56*x^22 + 126*x^21 + 60*x^20 + 67*x^19 + 24*x^18 + 43*x^17 + 50*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 18*x^8 + 22*x^7 + 88*x^6 + 78*x^5 + 60*x^4 + 101*x^3 + 120*x^2 + 109*x + 46, x^27 + 33*x^25 + 110*x^24 + 38*x^23 + 56*x^22 + 62*x^21 + 60*x^20 + 67*x^19 + 24*x^18 + 107*x^17 + 82*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 114*x^8 + 22*x^7 + 88*x^6 + 14*x^5 + 60*x^4 + 101*x^3 + 120*x^2 + 45*x + 14, x^27 + 33*x^25 + 18*x^24 + 6*x^23 + 72*x^22 + 94*x^21 + 4*x^20 + 99*x^19 + 104*x^18 + 75*x^17 + 110*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 14*x^8 + 118*x^7 + 40*x^6 + 46*x^5 + 4*x^4 + 5*x^3 + 8*x^2 + 13*x + 50, x^27 + 33*x^25 + 98*x^24 + 22*x^23 + 56*x^22 + 110*x^21 + 20*x^20 + 83*x^19 + 120*x^18 + 59*x^17 + 46*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 94*x^8 + 70*x^7 + 88*x^6 + 126*x^5 + 84*x^4 + 53*x^3 + 88*x^2 + 61*x + 82, x^27 + 33*x^25 + 82*x^24 + 38*x^23 + 40*x^22 + 62*x^21 + 36*x^20 + 67*x^19 + 8*x^18 + 107*x^17 + 14*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 14*x^8 + 22*x^7 + 8*x^6 + 14*x^5 + 36*x^4 + 101*x^3 + 40*x^2 + 45*x + 82, x^27 + 33*x^25 + 62*x^24 + 118*x^23 + 72*x^22 + 78*x^21 + 44*x^20 + 115*x^19 + 8*x^18 + 91*x^17 + 50*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 2*x^8 + 38*x^7 + 40*x^6 + 94*x^5 + 108*x^4 + 85*x^3 + 40*x^2 + 93*x + 78, x^27 + 33*x^25 + 26*x^24 + 70*x^23 + 120*x^22 + 62*x^21 + 68*x^20 + 99*x^19 + 56*x^18 + 43*x^17 + 118*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 38*x^8 + 54*x^7 + 24*x^6 + 14*x^5 + 4*x^4 + 5*x^3 + 24*x^2 + 109*x + 10, x^27 + 33*x^25 + 62*x^24 + 70*x^23 + 120*x^22 + 30*x^21 + 28*x^20 + 35*x^19 + 88*x^18 + 11*x^17 + 66*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 34*x^8 + 54*x^7 + 24*x^6 + 110*x^5 + 28*x^4 + 69*x^3 + 56*x^2 + 77*x + 30, x^27 + 33*x^25 + 6*x^24 + 54*x^23 + 120*x^22 + 110*x^21 + 108*x^20 + 115*x^19 + 88*x^18 + 123*x^17 + 122*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 90*x^8 + 102*x^7 + 24*x^6 + 126*x^5 + 108*x^4 + 85*x^3 + 56*x^2 + 125*x + 102, x^27 + 33*x^25 + 50*x^24 + 38*x^23 + 104*x^22 + 62*x^21 + 36*x^20 + 67*x^19 + 72*x^18 + 107*x^17 + 110*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 46*x^8 + 22*x^7 + 72*x^6 + 14*x^5 + 36*x^4 + 101*x^3 + 104*x^2 + 45*x + 114, x^27 + 33*x^25 + 126*x^24 + 118*x^23 + 40*x^22 + 14*x^21 + 76*x^20 + 115*x^19 + 40*x^18 + 27*x^17 + 82*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 2*x^8 + 38*x^7 + 8*x^6 + 30*x^5 + 12*x^4 + 85*x^3 + 72*x^2 + 29*x + 110, x^27 + 33*x^25 + 94*x^24 + 54*x^23 + 40*x^22 + 78*x^21 + 12*x^20 + 51*x^19 + 40*x^18 + 91*x^17 + 114*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 34*x^8 + 102*x^7 + 8*x^6 + 94*x^5 + 76*x^4 + 21*x^3 + 72*x^2 + 93*x + 78, x^27 + 33*x^25 + 82*x^24 + 118*x^23 + 56*x^22 + 78*x^21 + 52*x^20 + 115*x^19 + 120*x^18 + 91*x^17 + 126*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 110*x^8 + 38*x^7 + 88*x^6 + 94*x^5 + 116*x^4 + 85*x^3 + 88*x^2 + 93*x + 2, x^27 + 33*x^25 + 102*x^24 + 118*x^23 + 88*x^22 + 110*x^21 + 76*x^20 + 51*x^19 + 120*x^18 + 123*x^17 + 122*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 58*x^8 + 38*x^7 + 120*x^6 + 126*x^5 + 76*x^4 + 21*x^3 + 88*x^2 + 125*x + 38, x^27 + 33*x^25 + 70*x^24 + 54*x^23 + 120*x^22 + 46*x^21 + 44*x^20 + 115*x^19 + 88*x^18 + 59*x^17 + 122*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 26*x^8 + 102*x^7 + 24*x^6 + 62*x^5 + 44*x^4 + 85*x^3 + 56*x^2 + 61*x + 102, x^27 + 33*x^25 + 78*x^24 + 38*x^23 + 88*x^22 + 62*x^21 + 28*x^20 + 67*x^19 + 120*x^18 + 107*x^17 + 82*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 82*x^8 + 22*x^7 + 120*x^6 + 14*x^5 + 28*x^4 + 101*x^3 + 88*x^2 + 45*x + 78, x^27 + 33*x^25 + 94*x^24 + 102*x^23 + 56*x^22 + 126*x^21 + 92*x^20 + 3*x^19 + 24*x^18 + 43*x^17 + 34*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 2*x^8 + 86*x^7 + 88*x^6 + 78*x^5 + 92*x^4 + 37*x^3 + 120*x^2 + 109*x + 62, x^27 + 33*x^25 + 122*x^24 + 6*x^23 + 88*x^22 + 126*x^21 + 100*x^20 + 35*x^19 + 88*x^18 + 107*x^17 + 54*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 6*x^8 + 118*x^7 + 120*x^6 + 78*x^5 + 36*x^4 + 69*x^3 + 56*x^2 + 45*x + 10, x^27 + 33*x^25 + 14*x^24 + 22*x^23 + 40*x^22 + 110*x^21 + 108*x^20 + 83*x^19 + 40*x^18 + 59*x^17 + 66*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 114*x^8 + 70*x^7 + 8*x^6 + 126*x^5 + 44*x^4 + 53*x^3 + 72*x^2 + 61*x + 126, x^27 + 33*x^25 + 10*x^24 + 6*x^23 + 24*x^22 + 62*x^21 + 68*x^20 + 35*x^19 + 24*x^18 + 43*x^17 + 102*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 118*x^8 + 118*x^7 + 56*x^6 + 14*x^5 + 4*x^4 + 69*x^3 + 120*x^2 + 109*x + 90, x^27 + 33*x^25 + 2*x^24 + 22*x^23 + 56*x^22 + 46*x^21 + 20*x^20 + 83*x^19 + 120*x^18 + 123*x^17 + 78*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 62*x^8 + 70*x^7 + 88*x^6 + 62*x^5 + 84*x^4 + 53*x^3 + 88*x^2 + 125*x + 50, x^27 + 33*x^25 + 94*x^24 + 54*x^23 + 72*x^22 + 14*x^21 + 108*x^20 + 51*x^19 + 8*x^18 + 27*x^17 + 18*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 98*x^8 + 102*x^7 + 40*x^6 + 30*x^5 + 44*x^4 + 21*x^3 + 40*x^2 + 29*x + 110, x^27 + 33*x^25 + 26*x^24 + 38*x^23 + 88*x^22 + 94*x^21 + 100*x^20 + 3*x^19 + 88*x^18 + 11*x^17 + 86*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 102*x^8 + 22*x^7 + 120*x^6 + 46*x^5 + 36*x^4 + 37*x^3 + 56*x^2 + 77*x + 106, x^27 + 33*x^25 + 118*x^24 + 54*x^23 + 56*x^22 + 110*x^21 + 76*x^20 + 115*x^19 + 24*x^18 + 123*x^17 + 10*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 106*x^8 + 102*x^7 + 88*x^6 + 126*x^5 + 76*x^4 + 85*x^3 + 120*x^2 + 125*x + 86, x^27 + 33*x^25 + 102*x^24 + 86*x^23 + 88*x^22 + 78*x^21 + 76*x^20 + 83*x^19 + 120*x^18 + 27*x^17 + 122*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 58*x^8 + 6*x^7 + 120*x^6 + 94*x^5 + 76*x^4 + 53*x^3 + 88*x^2 + 29*x + 38, x^27 + 33*x^25 + 18*x^24 + 22*x^23 + 56*x^22 + 46*x^21 + 116*x^20 + 83*x^19 + 120*x^18 + 123*x^17 + 126*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 46*x^8 + 70*x^7 + 88*x^6 + 62*x^5 + 52*x^4 + 53*x^3 + 88*x^2 + 125*x + 2, x^27 + 33*x^25 + 114*x^24 + 86*x^23 + 88*x^22 + 110*x^21 + 84*x^20 + 19*x^19 + 88*x^18 + 59*x^17 + 126*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 14*x^8 + 6*x^7 + 120*x^6 + 126*x^5 + 20*x^4 + 117*x^3 + 56*x^2 + 61*x + 66, x^27 + 33*x^25 + 90*x^24 + 118*x^23 + 40*x^22 + 46*x^21 + 116*x^20 + 51*x^19 + 8*x^18 + 59*x^17 + 6*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 6*x^8 + 38*x^7 + 8*x^6 + 62*x^5 + 116*x^4 + 21*x^3 + 40*x^2 + 61*x + 90, x^27 + 33*x^25 + 6*x^24 + 118*x^23 + 24*x^22 + 110*x^21 + 76*x^20 + 51*x^19 + 56*x^18 + 123*x^17 + 26*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 26*x^8 + 38*x^7 + 56*x^6 + 126*x^5 + 76*x^4 + 21*x^3 + 24*x^2 + 125*x + 6, x^27 + 33*x^25 + 118*x^24 + 86*x^23 + 88*x^22 + 14*x^21 + 108*x^20 + 83*x^19 + 120*x^18 + 91*x^17 + 106*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 42*x^8 + 6*x^7 + 120*x^6 + 30*x^5 + 108*x^4 + 53*x^3 + 88*x^2 + 93*x + 54, x^27 + 33*x^25 + 102*x^24 + 70*x^23 + 8*x^22 + 62*x^21 + 60*x^20 + 99*x^19 + 72*x^18 + 43*x^17 + 10*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 90*x^8 + 54*x^7 + 104*x^6 + 14*x^5 + 124*x^4 + 5*x^3 + 104*x^2 + 109*x + 118, x^27 + 33*x^25 + 110*x^24 + 86*x^23 + 72*x^22 + 46*x^21 + 76*x^20 + 19*x^19 + 8*x^18 + 123*x^17 + 66*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 82*x^8 + 6*x^7 + 40*x^6 + 62*x^5 + 12*x^4 + 117*x^3 + 40*x^2 + 125*x + 62, x^27 + 33*x^25 + 30*x^24 + 38*x^23 + 24*x^22 + 62*x^21 + 60*x^20 + 67*x^19 + 56*x^18 + 107*x^17 + 2*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 2*x^8 + 22*x^7 + 56*x^6 + 14*x^5 + 60*x^4 + 101*x^3 + 24*x^2 + 45*x + 30, x^27 + 33*x^25 + 6*x^24 + 102*x^23 + 72*x^22 + 30*x^21 + 124*x^20 + 67*x^19 + 8*x^18 + 75*x^17 + 106*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 58*x^8 + 86*x^7 + 40*x^6 + 110*x^5 + 60*x^4 + 101*x^3 + 40*x^2 + 13*x + 22, x^27 + 33*x^25 + 62*x^24 + 118*x^23 + 72*x^22 + 14*x^21 + 108*x^20 + 115*x^19 + 8*x^18 + 27*x^17 + 114*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 2*x^8 + 38*x^7 + 40*x^6 + 30*x^5 + 44*x^4 + 85*x^3 + 40*x^2 + 29*x + 14, x^27 + 33*x^25 + 118*x^24 + 6*x^23 + 104*x^22 + 126*x^21 + 124*x^20 + 35*x^19 + 104*x^18 + 107*x^17 + 90*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 10*x^8 + 118*x^7 + 72*x^6 + 78*x^5 + 60*x^4 + 69*x^3 + 8*x^2 + 45*x + 102, x^27 + 33*x^25 + 54*x^24 + 54*x^23 + 88*x^22 + 46*x^21 + 44*x^20 + 115*x^19 + 120*x^18 + 59*x^17 + 106*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 106*x^8 + 102*x^7 + 120*x^6 + 62*x^5 + 44*x^4 + 85*x^3 + 88*x^2 + 61*x + 54, x^27 + 33*x^25 + 62*x^24 + 86*x^23 + 40*x^22 + 110*x^21 + 76*x^20 + 19*x^19 + 40*x^18 + 59*x^17 + 18*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 66*x^8 + 6*x^7 + 8*x^6 + 126*x^5 + 12*x^4 + 117*x^3 + 72*x^2 + 61*x + 46, x^27 + 33*x^25 + 50*x^24 + 38*x^23 + 8*x^22 + 126*x^21 + 4*x^20 + 67*x^19 + 40*x^18 + 43*x^17 + 14*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 110*x^8 + 22*x^7 + 104*x^6 + 78*x^5 + 4*x^4 + 101*x^3 + 72*x^2 + 109*x + 18, x^27 + 33*x^25 + 78*x^24 + 22*x^23 + 72*x^22 + 46*x^21 + 76*x^20 + 83*x^19 + 8*x^18 + 123*x^17 + 34*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 114*x^8 + 70*x^7 + 40*x^6 + 62*x^5 + 12*x^4 + 53*x^3 + 40*x^2 + 125*x + 94, x^27 + 33*x^25 + 122*x^24 + 38*x^23 + 56*x^22 + 30*x^21 + 68*x^20 + 3*x^19 + 120*x^18 + 75*x^17 + 86*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 70*x^8 + 22*x^7 + 88*x^6 + 110*x^5 + 4*x^4 + 37*x^3 + 88*x^2 + 13*x + 42, x^27 + 33*x^25 + 78*x^24 + 54*x^23 + 104*x^22 + 78*x^21 + 108*x^20 + 51*x^19 + 104*x^18 + 91*x^17 + 2*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 50*x^8 + 102*x^7 + 72*x^6 + 94*x^5 + 44*x^4 + 21*x^3 + 8*x^2 + 93*x + 62, x^27 + 33*x^25 + 86*x^24 + 22*x^23 + 120*x^22 + 14*x^21 + 12*x^20 + 19*x^19 + 88*x^18 + 91*x^17 + 42*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 10*x^8 + 70*x^7 + 24*x^6 + 30*x^5 + 12*x^4 + 117*x^3 + 56*x^2 + 93*x + 54, x^27 + 33*x^25 + 70*x^24 + 118*x^23 + 56*x^22 + 110*x^21 + 108*x^20 + 51*x^19 + 24*x^18 + 123*x^17 + 58*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 26*x^8 + 38*x^7 + 88*x^6 + 126*x^5 + 108*x^4 + 21*x^3 + 120*x^2 + 125*x + 38, x^27 + 33*x^25 + 98*x^24 + 54*x^23 + 120*x^22 + 14*x^21 + 84*x^20 + 51*x^19 + 56*x^18 + 27*x^17 + 110*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 94*x^8 + 102*x^7 + 24*x^6 + 30*x^5 + 20*x^4 + 21*x^3 + 24*x^2 + 29*x + 18, x^27 + 33*x^25 + 66*x^24 + 54*x^23 + 56*x^22 + 78*x^21 + 20*x^20 + 51*x^19 + 120*x^18 + 91*x^17 + 14*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 126*x^8 + 102*x^7 + 88*x^6 + 94*x^5 + 84*x^4 + 21*x^3 + 88*x^2 + 93*x + 114, x^27 + 33*x^25 + 122*x^24 + 118*x^23 + 104*x^22 + 110*x^21 + 52*x^20 + 51*x^19 + 72*x^18 + 123*x^17 + 102*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 102*x^8 + 38*x^7 + 72*x^6 + 126*x^5 + 52*x^4 + 21*x^3 + 104*x^2 + 125*x + 122, x^27 + 33*x^25 + 10*x^24 + 70*x^23 + 88*x^22 + 126*x^21 + 4*x^20 + 99*x^19 + 88*x^18 + 107*x^17 + 38*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 118*x^8 + 54*x^7 + 120*x^6 + 78*x^5 + 68*x^4 + 5*x^3 + 56*x^2 + 45*x + 26, x^27 + 33*x^25 + 102*x^24 + 102*x^23 + 104*x^22 + 30*x^21 + 92*x^20 + 67*x^19 + 104*x^18 + 75*x^17 + 106*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 26*x^8 + 86*x^7 + 72*x^6 + 110*x^5 + 28*x^4 + 101*x^3 + 8*x^2 + 13*x + 86, x^27 + 33*x^25 + 62*x^24 + 86*x^23 + 72*x^22 + 46*x^21 + 44*x^20 + 19*x^19 + 8*x^18 + 123*x^17 + 50*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 2*x^8 + 6*x^7 + 40*x^6 + 62*x^5 + 108*x^4 + 117*x^3 + 40*x^2 + 125*x + 78, x^27 + 33*x^25 + 46*x^24 + 38*x^23 + 56*x^22 + 126*x^21 + 124*x^20 + 67*x^19 + 24*x^18 + 43*x^17 + 82*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 50*x^8 + 22*x^7 + 88*x^6 + 78*x^5 + 124*x^4 + 101*x^3 + 120*x^2 + 109*x + 14, x^27 + 33*x^25 + 38*x^24 + 102*x^23 + 8*x^22 + 94*x^21 + 60*x^20 + 67*x^19 + 72*x^18 + 11*x^17 + 74*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 26*x^8 + 86*x^7 + 104*x^6 + 46*x^5 + 124*x^4 + 101*x^3 + 104*x^2 + 77*x + 54, x^27 + 33*x^25 + 10*x^24 + 86*x^23 + 8*x^22 + 14*x^21 + 116*x^20 + 83*x^19 + 40*x^18 + 91*x^17 + 54*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 22*x^8 + 6*x^7 + 104*x^6 + 30*x^5 + 116*x^4 + 53*x^3 + 72*x^2 + 93*x + 106, x^27 + 33*x^25 + 2*x^24 + 102*x^23 + 40*x^22 + 126*x^21 + 68*x^20 + 3*x^19 + 8*x^18 + 43*x^17 + 30*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 94*x^8 + 86*x^7 + 8*x^6 + 78*x^5 + 68*x^4 + 37*x^3 + 40*x^2 + 109*x + 66, x^27 + 33*x^25 + 94*x^24 + 86*x^23 + 40*x^22 + 110*x^21 + 12*x^20 + 19*x^19 + 40*x^18 + 59*x^17 + 114*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 34*x^8 + 6*x^7 + 8*x^6 + 126*x^5 + 76*x^4 + 117*x^3 + 72*x^2 + 61*x + 78, x^27 + 33*x^25 + 62*x^24 + 70*x^23 + 56*x^22 + 30*x^21 + 92*x^20 + 35*x^19 + 24*x^18 + 11*x^17 + 2*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 34*x^8 + 54*x^7 + 88*x^6 + 110*x^5 + 92*x^4 + 69*x^3 + 120*x^2 + 77*x + 94, x^27 + 33*x^25 + 34*x^24 + 54*x^23 + 88*x^22 + 14*x^21 + 52*x^20 + 51*x^19 + 88*x^18 + 27*x^17 + 78*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 94*x^8 + 102*x^7 + 120*x^6 + 30*x^5 + 116*x^4 + 21*x^3 + 56*x^2 + 29*x + 114, x^27 + 33*x^25 + 30*x^24 + 54*x^23 + 40*x^22 + 14*x^21 + 76*x^20 + 51*x^19 + 40*x^18 + 27*x^17 + 114*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 98*x^8 + 102*x^7 + 8*x^6 + 30*x^5 + 12*x^4 + 21*x^3 + 72*x^2 + 29*x + 78, x^27 + 33*x^25 + 50*x^24 + 102*x^23 + 8*x^22 + 126*x^21 + 68*x^20 + 3*x^19 + 40*x^18 + 43*x^17 + 78*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 110*x^8 + 86*x^7 + 104*x^6 + 78*x^5 + 68*x^4 + 37*x^3 + 72*x^2 + 109*x + 82, x^27 + 33*x^25 + 34*x^24 + 38*x^23 + 72*x^22 + 62*x^21 + 36*x^20 + 67*x^19 + 104*x^18 + 107*x^17 + 94*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 126*x^8 + 22*x^7 + 40*x^6 + 14*x^5 + 36*x^4 + 101*x^3 + 8*x^2 + 45*x + 66, x^27 + 33*x^25 + 58*x^24 + 70*x^23 + 88*x^22 + 126*x^21 + 36*x^20 + 99*x^19 + 88*x^18 + 107*x^17 + 54*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 70*x^8 + 54*x^7 + 120*x^6 + 78*x^5 + 100*x^4 + 5*x^3 + 56*x^2 + 45*x + 10, x^27 + 33*x^25 + 82*x^24 + 118*x^23 + 88*x^22 + 78*x^21 + 84*x^20 + 115*x^19 + 88*x^18 + 91*x^17 + 94*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 46*x^8 + 38*x^7 + 120*x^6 + 94*x^5 + 20*x^4 + 85*x^3 + 56*x^2 + 93*x + 98, x^27 + 33*x^25 + 122*x^24 + 102*x^23 + 56*x^22 + 94*x^21 + 68*x^20 + 67*x^19 + 120*x^18 + 11*x^17 + 86*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 70*x^8 + 86*x^7 + 88*x^6 + 46*x^5 + 4*x^4 + 101*x^3 + 88*x^2 + 77*x + 42, x^27 + 33*x^25 + 46*x^24 + 118*x^23 + 40*x^22 + 14*x^21 + 108*x^20 + 115*x^19 + 40*x^18 + 27*x^17 + 98*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 82*x^8 + 38*x^7 + 8*x^6 + 30*x^5 + 44*x^4 + 85*x^3 + 72*x^2 + 29*x + 94, x^27 + 33*x^25 + 18*x^24 + 6*x^23 + 40*x^22 + 30*x^21 + 36*x^20 + 99*x^19 + 8*x^18 + 11*x^17 + 78*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 78*x^8 + 118*x^7 + 8*x^6 + 110*x^5 + 36*x^4 + 5*x^3 + 40*x^2 + 77*x + 18, x^27 + 33*x^25 + 30*x^24 + 6*x^23 + 88*x^22 + 94*x^21 + 60*x^20 + 99*x^19 + 120*x^18 + 75*x^17 + 2*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 2*x^8 + 118*x^7 + 120*x^6 + 46*x^5 + 60*x^4 + 5*x^3 + 88*x^2 + 13*x + 30, x^27 + 33*x^25 + 26*x^24 + 70*x^23 + 56*x^22 + 62*x^21 + 4*x^20 + 99*x^19 + 120*x^18 + 43*x^17 + 54*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 38*x^8 + 54*x^7 + 88*x^6 + 14*x^5 + 68*x^4 + 5*x^3 + 88*x^2 + 109*x + 74, x^27 + 33*x^25 + 14*x^24 + 22*x^23 + 8*x^22 + 110*x^21 + 76*x^20 + 83*x^19 + 72*x^18 + 59*x^17 + 98*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 50*x^8 + 70*x^7 + 104*x^6 + 126*x^5 + 12*x^4 + 53*x^3 + 104*x^2 + 61*x + 30, x^27 + 33*x^25 + 126*x^24 + 86*x^23 + 104*x^22 + 46*x^21 + 76*x^20 + 19*x^19 + 104*x^18 + 123*x^17 + 82*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 2*x^8 + 6*x^7 + 72*x^6 + 62*x^5 + 12*x^4 + 117*x^3 + 8*x^2 + 125*x + 110, x^27 + 33*x^25 + 98*x^24 + 86*x^23 + 56*x^22 + 46*x^21 + 20*x^20 + 19*x^19 + 120*x^18 + 123*x^17 + 46*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 94*x^8 + 6*x^7 + 88*x^6 + 62*x^5 + 84*x^4 + 117*x^3 + 88*x^2 + 125*x + 82, x^27 + 33*x^25 + 30*x^24 + 54*x^23 + 72*x^22 + 78*x^21 + 44*x^20 + 51*x^19 + 8*x^18 + 91*x^17 + 18*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 34*x^8 + 102*x^7 + 40*x^6 + 94*x^5 + 108*x^4 + 21*x^3 + 40*x^2 + 93*x + 110, x^27 + 33*x^25 + 38*x^24 + 38*x^23 + 104*x^22 + 94*x^21 + 92*x^20 + 3*x^19 + 104*x^18 + 11*x^17 + 42*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 90*x^8 + 22*x^7 + 72*x^6 + 46*x^5 + 28*x^4 + 37*x^3 + 8*x^2 + 77*x + 22, x^27 + 33*x^25 + 86*x^24 + 86*x^23 + 24*x^22 + 78*x^21 + 44*x^20 + 83*x^19 + 56*x^18 + 27*x^17 + 10*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 74*x^8 + 6*x^7 + 56*x^6 + 94*x^5 + 44*x^4 + 53*x^3 + 24*x^2 + 29*x + 22, x^27 + 33*x^25 + 118*x^24 + 102*x^23 + 8*x^22 + 94*x^21 + 28*x^20 + 67*x^19 + 72*x^18 + 11*x^17 + 58*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 74*x^8 + 86*x^7 + 104*x^6 + 46*x^5 + 92*x^4 + 101*x^3 + 104*x^2 + 77*x + 70, x^27 + 33*x^25 + 118*x^24 + 54*x^23 + 24*x^22 + 46*x^21 + 108*x^20 + 115*x^19 + 56*x^18 + 59*x^17 + 106*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 42*x^8 + 102*x^7 + 56*x^6 + 62*x^5 + 108*x^4 + 85*x^3 + 24*x^2 + 61*x + 54, x^27 + 33*x^25 + 110*x^24 + 70*x^23 + 24*x^22 + 30*x^21 + 92*x^20 + 35*x^19 + 56*x^18 + 11*x^17 + 50*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 50*x^8 + 54*x^7 + 56*x^6 + 110*x^5 + 92*x^4 + 69*x^3 + 24*x^2 + 77*x + 110, x^27 + 33*x^25 + 98*x^24 + 118*x^23 + 24*x^22 + 78*x^21 + 116*x^20 + 115*x^19 + 24*x^18 + 91*x^17 + 78*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 30*x^8 + 38*x^7 + 56*x^6 + 94*x^5 + 52*x^4 + 85*x^3 + 120*x^2 + 93*x + 114, x^27 + 33*x^25 + 46*x^24 + 118*x^23 + 72*x^22 + 14*x^21 + 12*x^20 + 115*x^19 + 8*x^18 + 27*x^17 + 66*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 18*x^8 + 38*x^7 + 40*x^6 + 30*x^5 + 76*x^4 + 85*x^3 + 40*x^2 + 29*x + 62, x^27 + 33*x^25 + 82*x^24 + 102*x^23 + 8*x^22 + 62*x^21 + 68*x^20 + 3*x^19 + 40*x^18 + 107*x^17 + 110*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 78*x^8 + 86*x^7 + 104*x^6 + 14*x^5 + 68*x^4 + 37*x^3 + 72*x^2 + 45*x + 50, x^27 + 33*x^25 + 30*x^24 + 38*x^23 + 88*x^22 + 62*x^21 + 124*x^20 + 67*x^19 + 120*x^18 + 107*x^17 + 66*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 2*x^8 + 22*x^7 + 120*x^6 + 14*x^5 + 124*x^4 + 101*x^3 + 88*x^2 + 45*x + 94, x^27 + 33*x^25 + 34*x^24 + 6*x^23 + 72*x^22 + 94*x^21 + 100*x^20 + 99*x^19 + 104*x^18 + 75*x^17 + 30*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 126*x^8 + 118*x^7 + 40*x^6 + 46*x^5 + 100*x^4 + 5*x^3 + 8*x^2 + 13*x + 2, x^27 + 33*x^25 + 102*x^24 + 102*x^23 + 8*x^22 + 94*x^21 + 60*x^20 + 67*x^19 + 72*x^18 + 11*x^17 + 10*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 90*x^8 + 86*x^7 + 104*x^6 + 46*x^5 + 124*x^4 + 101*x^3 + 104*x^2 + 77*x + 118, x^27 + 33*x^25 + 22*x^24 + 70*x^23 + 8*x^22 + 62*x^21 + 92*x^20 + 99*x^19 + 72*x^18 + 43*x^17 + 26*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 42*x^8 + 54*x^7 + 104*x^6 + 14*x^5 + 28*x^4 + 5*x^3 + 104*x^2 + 109*x + 102, x^27 + 33*x^25 + 2*x^24 + 6*x^23 + 8*x^22 + 94*x^21 + 100*x^20 + 99*x^19 + 40*x^18 + 75*x^17 + 126*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 30*x^8 + 118*x^7 + 104*x^6 + 46*x^5 + 100*x^4 + 5*x^3 + 72*x^2 + 13*x + 34, x^27 + 33*x^25 + 66*x^24 + 70*x^23 + 8*x^22 + 94*x^21 + 36*x^20 + 35*x^19 + 40*x^18 + 75*x^17 + 126*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 94*x^8 + 54*x^7 + 104*x^6 + 46*x^5 + 36*x^4 + 69*x^3 + 72*x^2 + 13*x + 34, x^27 + 33*x^25 + 34*x^24 + 86*x^23 + 88*x^22 + 110*x^21 + 116*x^20 + 19*x^19 + 88*x^18 + 59*x^17 + 14*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 94*x^8 + 6*x^7 + 120*x^6 + 126*x^5 + 52*x^4 + 117*x^3 + 56*x^2 + 61*x + 50, x^27 + 33*x^25 + 118*x^24 + 54*x^23 + 56*x^22 + 46*x^21 + 12*x^20 + 115*x^19 + 24*x^18 + 59*x^17 + 74*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 106*x^8 + 102*x^7 + 88*x^6 + 62*x^5 + 12*x^4 + 85*x^3 + 120*x^2 + 61*x + 22, x^27 + 33*x^25 + 22*x^24 + 22*x^23 + 120*x^22 + 78*x^21 + 76*x^20 + 19*x^19 + 88*x^18 + 27*x^17 + 42*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 74*x^8 + 70*x^7 + 24*x^6 + 94*x^5 + 76*x^4 + 117*x^3 + 56*x^2 + 29*x + 54, x^27 + 33*x^25 + 14*x^24 + 102*x^23 + 56*x^22 + 126*x^21 + 124*x^20 + 3*x^19 + 24*x^18 + 43*x^17 + 50*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 82*x^8 + 86*x^7 + 88*x^6 + 78*x^5 + 124*x^4 + 37*x^3 + 120*x^2 + 109*x + 46, x^27 + 33*x^25 + 78*x^24 + 22*x^23 + 72*x^22 + 110*x^21 + 12*x^20 + 83*x^19 + 8*x^18 + 59*x^17 + 98*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 114*x^8 + 70*x^7 + 40*x^6 + 126*x^5 + 76*x^4 + 53*x^3 + 40*x^2 + 61*x + 30, x^27 + 33*x^25 + 2*x^24 + 6*x^23 + 104*x^22 + 30*x^21 + 4*x^20 + 99*x^19 + 72*x^18 + 11*x^17 + 94*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 94*x^8 + 118*x^7 + 72*x^6 + 110*x^5 + 4*x^4 + 5*x^3 + 104*x^2 + 77*x + 2, x^27 + 33*x^25 + 126*x^24 + 70*x^23 + 120*x^22 + 30*x^21 + 28*x^20 + 35*x^19 + 88*x^18 + 11*x^17 + 2*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 98*x^8 + 54*x^7 + 24*x^6 + 110*x^5 + 28*x^4 + 69*x^3 + 56*x^2 + 77*x + 94, x^27 + 33*x^25 + 10*x^24 + 6*x^23 + 120*x^22 + 62*x^21 + 36*x^20 + 35*x^19 + 56*x^18 + 43*x^17 + 6*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 54*x^8 + 118*x^7 + 24*x^6 + 14*x^5 + 100*x^4 + 69*x^3 + 24*x^2 + 109*x + 122, x^27 + 33*x^25 + 50*x^24 + 102*x^23 + 8*x^22 + 62*x^21 + 4*x^20 + 3*x^19 + 40*x^18 + 107*x^17 + 14*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 110*x^8 + 86*x^7 + 104*x^6 + 14*x^5 + 4*x^4 + 37*x^3 + 72*x^2 + 45*x + 18, x^27 + 33*x^25 + 70*x^24 + 102*x^23 + 40*x^22 + 94*x^21 + 28*x^20 + 67*x^19 + 40*x^18 + 11*x^17 + 10*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 58*x^8 + 86*x^7 + 8*x^6 + 46*x^5 + 92*x^4 + 101*x^3 + 72*x^2 + 77*x + 54, x^27 + 33*x^25 + 86*x^24 + 22*x^23 + 24*x^22 + 78*x^21 + 108*x^20 + 19*x^19 + 56*x^18 + 27*x^17 + 74*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 74*x^8 + 70*x^7 + 56*x^6 + 94*x^5 + 108*x^4 + 117*x^3 + 24*x^2 + 29*x + 86, x^27 + 33*x^25 + 98*x^24 + 102*x^23 + 104*x^22 + 126*x^21 + 68*x^20 + 3*x^19 + 72*x^18 + 43*x^17 + 126*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 126*x^8 + 86*x^7 + 72*x^6 + 78*x^5 + 68*x^4 + 37*x^3 + 104*x^2 + 109*x + 98, x^27 + 33*x^25 + 18*x^24 + 38*x^23 + 72*x^22 + 126*x^21 + 4*x^20 + 67*x^19 + 104*x^18 + 43*x^17 + 110*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 14*x^8 + 22*x^7 + 40*x^6 + 78*x^5 + 4*x^4 + 101*x^3 + 8*x^2 + 109*x + 50, x^27 + 33*x^25 + 46*x^24 + 38*x^23 + 56*x^22 + 62*x^21 + 60*x^20 + 67*x^19 + 24*x^18 + 107*x^17 + 18*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 50*x^8 + 22*x^7 + 88*x^6 + 14*x^5 + 60*x^4 + 101*x^3 + 120*x^2 + 45*x + 78, x^27 + 33*x^25 + 58*x^24 + 22*x^23 + 8*x^22 + 14*x^21 + 84*x^20 + 19*x^19 + 40*x^18 + 91*x^17 + 6*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 102*x^8 + 70*x^7 + 104*x^6 + 30*x^5 + 84*x^4 + 117*x^3 + 72*x^2 + 93*x + 26, x^27 + 33*x^25 + 114*x^24 + 54*x^23 + 24*x^22 + 14*x^21 + 84*x^20 + 51*x^19 + 24*x^18 + 27*x^17 + 126*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 14*x^8 + 102*x^7 + 56*x^6 + 30*x^5 + 20*x^4 + 21*x^3 + 120*x^2 + 29*x + 66, x^27 + 33*x^25 + 94*x^24 + 70*x^23 + 88*x^22 + 94*x^21 + 124*x^20 + 35*x^19 + 120*x^18 + 75*x^17 + 2*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 66*x^8 + 54*x^7 + 120*x^6 + 46*x^5 + 124*x^4 + 69*x^3 + 88*x^2 + 13*x + 30, x^27 + 33*x^25 + 42*x^24 + 54*x^23 + 8*x^22 + 46*x^21 + 116*x^20 + 115*x^19 + 40*x^18 + 59*x^17 + 86*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 118*x^8 + 102*x^7 + 104*x^6 + 62*x^5 + 116*x^4 + 85*x^3 + 72*x^2 + 61*x + 74, x^27 + 33*x^25 + 66*x^24 + 86*x^23 + 56*x^22 + 110*x^21 + 20*x^20 + 19*x^19 + 120*x^18 + 59*x^17 + 14*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 126*x^8 + 6*x^7 + 88*x^6 + 126*x^5 + 84*x^4 + 117*x^3 + 88*x^2 + 61*x + 114, x^27 + 33*x^25 + 30*x^24 + 86*x^23 + 40*x^22 + 46*x^21 + 76*x^20 + 19*x^19 + 40*x^18 + 123*x^17 + 114*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 98*x^8 + 6*x^7 + 8*x^6 + 62*x^5 + 12*x^4 + 117*x^3 + 72*x^2 + 125*x + 78, x^27 + 33*x^25 + 38*x^24 + 54*x^23 + 88*x^22 + 110*x^21 + 12*x^20 + 115*x^19 + 120*x^18 + 123*x^17 + 122*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 122*x^8 + 102*x^7 + 120*x^6 + 126*x^5 + 12*x^4 + 85*x^3 + 88*x^2 + 125*x + 38, x^27 + 33*x^25 + 18*x^24 + 102*x^23 + 72*x^22 + 62*x^21 + 4*x^20 + 3*x^19 + 104*x^18 + 107*x^17 + 110*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 14*x^8 + 86*x^7 + 40*x^6 + 14*x^5 + 4*x^4 + 37*x^3 + 8*x^2 + 45*x + 50, x^27 + 33*x^25 + 50*x^24 + 118*x^23 + 24*x^22 + 78*x^21 + 84*x^20 + 115*x^19 + 24*x^18 + 91*x^17 + 62*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 78*x^8 + 38*x^7 + 56*x^6 + 94*x^5 + 20*x^4 + 85*x^3 + 120*x^2 + 93*x + 2, x^27 + 33*x^25 + 34*x^24 + 102*x^23 + 104*x^22 + 126*x^21 + 68*x^20 + 3*x^19 + 72*x^18 + 43*x^17 + 62*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 62*x^8 + 86*x^7 + 72*x^6 + 78*x^5 + 68*x^4 + 37*x^3 + 104*x^2 + 109*x + 34, x^27 + 33*x^25 + 90*x^24 + 118*x^23 + 40*x^22 + 110*x^21 + 52*x^20 + 51*x^19 + 8*x^18 + 123*x^17 + 70*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 6*x^8 + 38*x^7 + 8*x^6 + 126*x^5 + 52*x^4 + 21*x^3 + 40*x^2 + 125*x + 26, x^27 + 33*x^25 + 50*x^24 + 6*x^23 + 72*x^22 + 94*x^21 + 68*x^20 + 99*x^19 + 104*x^18 + 75*x^17 + 78*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 110*x^8 + 118*x^7 + 40*x^6 + 46*x^5 + 68*x^4 + 5*x^3 + 8*x^2 + 13*x + 82, x^27 + 33*x^25 + 22*x^24 + 6*x^23 + 104*x^22 + 62*x^21 + 124*x^20 + 35*x^19 + 104*x^18 + 43*x^17 + 122*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 106*x^8 + 118*x^7 + 72*x^6 + 14*x^5 + 60*x^4 + 69*x^3 + 8*x^2 + 109*x + 70, x^27 + 33*x^25 + 58*x^24 + 54*x^23 + 8*x^22 + 46*x^21 + 84*x^20 + 115*x^19 + 40*x^18 + 59*x^17 + 6*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 102*x^8 + 102*x^7 + 104*x^6 + 62*x^5 + 84*x^4 + 85*x^3 + 72*x^2 + 61*x + 26, x^27 + 33*x^25 + 58*x^24 + 70*x^23 + 56*x^22 + 126*x^21 + 4*x^20 + 99*x^19 + 120*x^18 + 107*x^17 + 86*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 6*x^8 + 54*x^7 + 88*x^6 + 78*x^5 + 68*x^4 + 5*x^3 + 88*x^2 + 45*x + 42, x^27 + 33*x^25 + 2*x^24 + 22*x^23 + 56*x^22 + 110*x^21 + 84*x^20 + 83*x^19 + 120*x^18 + 59*x^17 + 14*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 62*x^8 + 70*x^7 + 88*x^6 + 126*x^5 + 20*x^4 + 53*x^3 + 88*x^2 + 61*x + 114, x^27 + 33*x^25 + 118*x^24 + 38*x^23 + 8*x^22 + 94*x^21 + 92*x^20 + 3*x^19 + 72*x^18 + 11*x^17 + 122*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 74*x^8 + 22*x^7 + 104*x^6 + 46*x^5 + 28*x^4 + 37*x^3 + 104*x^2 + 77*x + 6, x^27 + 33*x^25 + 30*x^24 + 22*x^23 + 104*x^22 + 110*x^21 + 12*x^20 + 83*x^19 + 104*x^18 + 59*x^17 + 50*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 98*x^8 + 70*x^7 + 72*x^6 + 126*x^5 + 76*x^4 + 53*x^3 + 8*x^2 + 61*x + 14, x^27 + 33*x^25 + 18*x^24 + 38*x^23 + 40*x^22 + 126*x^21 + 100*x^20 + 67*x^19 + 8*x^18 + 43*x^17 + 14*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 78*x^8 + 22*x^7 + 8*x^6 + 78*x^5 + 100*x^4 + 101*x^3 + 40*x^2 + 109*x + 82, x^27 + 33*x^25 + 122*x^24 + 102*x^23 + 120*x^22 + 94*x^21 + 4*x^20 + 67*x^19 + 56*x^18 + 11*x^17 + 22*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 70*x^8 + 86*x^7 + 24*x^6 + 46*x^5 + 68*x^4 + 101*x^3 + 24*x^2 + 77*x + 106, x^27 + 33*x^25 + 10*x^24 + 22*x^23 + 72*x^22 + 78*x^21 + 52*x^20 + 19*x^19 + 104*x^18 + 27*x^17 + 118*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 22*x^8 + 70*x^7 + 40*x^6 + 94*x^5 + 52*x^4 + 117*x^3 + 8*x^2 + 29*x + 42, x^27 + 33*x^25 + 6*x^24 + 6*x^23 + 72*x^22 + 62*x^21 + 124*x^20 + 35*x^19 + 8*x^18 + 43*x^17 + 106*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 58*x^8 + 118*x^7 + 40*x^6 + 14*x^5 + 60*x^4 + 69*x^3 + 40*x^2 + 109*x + 22, x^27 + 33*x^25 + 58*x^24 + 118*x^23 + 8*x^22 + 110*x^21 + 84*x^20 + 51*x^19 + 40*x^18 + 123*x^17 + 6*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 102*x^8 + 38*x^7 + 104*x^6 + 126*x^5 + 84*x^4 + 21*x^3 + 72*x^2 + 125*x + 26, x^27 + 33*x^25 + 58*x^24 + 86*x^23 + 104*x^22 + 14*x^21 + 116*x^20 + 83*x^19 + 72*x^18 + 91*x^17 + 102*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 38*x^8 + 6*x^7 + 72*x^6 + 30*x^5 + 116*x^4 + 53*x^3 + 104*x^2 + 93*x + 122, x^27 + 33*x^25 + 54*x^24 + 70*x^23 + 72*x^22 + 62*x^21 + 92*x^20 + 99*x^19 + 8*x^18 + 43*x^17 + 58*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 10*x^8 + 54*x^7 + 40*x^6 + 14*x^5 + 28*x^4 + 5*x^3 + 40*x^2 + 109*x + 70, x^27 + 33*x^25 + 70*x^24 + 54*x^23 + 24*x^22 + 110*x^21 + 12*x^20 + 115*x^19 + 56*x^18 + 123*x^17 + 26*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 90*x^8 + 102*x^7 + 56*x^6 + 126*x^5 + 12*x^4 + 85*x^3 + 24*x^2 + 125*x + 6, x^27 + 33*x^25 + 66*x^24 + 6*x^23 + 40*x^22 + 94*x^21 + 4*x^20 + 99*x^19 + 8*x^18 + 75*x^17 + 30*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 30*x^8 + 118*x^7 + 8*x^6 + 46*x^5 + 4*x^4 + 5*x^3 + 40*x^2 + 13*x + 66, x^27 + 33*x^25 + 74*x^24 + 118*x^23 + 40*x^22 + 110*x^21 + 84*x^20 + 51*x^19 + 8*x^18 + 123*x^17 + 22*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 22*x^8 + 38*x^7 + 8*x^6 + 126*x^5 + 84*x^4 + 21*x^3 + 40*x^2 + 125*x + 74, x^27 + 33*x^25 + 54*x^24 + 22*x^23 + 56*x^22 + 14*x^21 + 12*x^20 + 19*x^19 + 24*x^18 + 91*x^17 + 10*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 42*x^8 + 70*x^7 + 88*x^6 + 30*x^5 + 12*x^4 + 117*x^3 + 120*x^2 + 93*x + 86, x^27 + 33*x^25 + 6*x^24 + 102*x^23 + 8*x^22 + 30*x^21 + 60*x^20 + 67*x^19 + 72*x^18 + 75*x^17 + 42*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 58*x^8 + 86*x^7 + 104*x^6 + 110*x^5 + 124*x^4 + 101*x^3 + 104*x^2 + 13*x + 86, x^27 + 33*x^25 + 118*x^24 + 118*x^23 + 24*x^22 + 110*x^21 + 108*x^20 + 51*x^19 + 56*x^18 + 123*x^17 + 106*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 42*x^8 + 38*x^7 + 56*x^6 + 126*x^5 + 108*x^4 + 21*x^3 + 24*x^2 + 125*x + 54, x^27 + 33*x^25 + 50*x^24 + 118*x^23 + 88*x^22 + 78*x^21 + 20*x^20 + 115*x^19 + 88*x^18 + 91*x^17 + 126*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 78*x^8 + 38*x^7 + 120*x^6 + 94*x^5 + 84*x^4 + 85*x^3 + 56*x^2 + 93*x + 66, x^27 + 33*x^25 + 62*x^24 + 70*x^23 + 24*x^22 + 94*x^21 + 124*x^20 + 35*x^19 + 56*x^18 + 75*x^17 + 98*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 98*x^8 + 54*x^7 + 56*x^6 + 46*x^5 + 124*x^4 + 69*x^3 + 24*x^2 + 13*x + 62, x^27 + 33*x^25 + 114*x^24 + 118*x^23 + 56*x^22 + 14*x^21 + 52*x^20 + 115*x^19 + 120*x^18 + 27*x^17 + 30*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 78*x^8 + 38*x^7 + 88*x^6 + 30*x^5 + 116*x^4 + 85*x^3 + 88*x^2 + 29*x + 98, x^27 + 33*x^25 + 38*x^24 + 54*x^23 + 120*x^22 + 110*x^21 + 44*x^20 + 115*x^19 + 88*x^18 + 123*x^17 + 90*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 58*x^8 + 102*x^7 + 24*x^6 + 126*x^5 + 44*x^4 + 85*x^3 + 56*x^2 + 125*x + 6, x^27 + 33*x^25 + 114*x^24 + 118*x^23 + 88*x^22 + 14*x^21 + 84*x^20 + 115*x^19 + 88*x^18 + 27*x^17 + 126*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 14*x^8 + 38*x^7 + 120*x^6 + 30*x^5 + 20*x^4 + 85*x^3 + 56*x^2 + 29*x + 66, x^27 + 33*x^25 + 26*x^24 + 22*x^23 + 72*x^22 + 78*x^21 + 20*x^20 + 19*x^19 + 104*x^18 + 27*x^17 + 38*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 6*x^8 + 70*x^7 + 40*x^6 + 94*x^5 + 20*x^4 + 117*x^3 + 8*x^2 + 29*x + 122, x^27 + 33*x^25 + 62*x^24 + 70*x^23 + 88*x^22 + 30*x^21 + 124*x^20 + 35*x^19 + 120*x^18 + 11*x^17 + 98*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 98*x^8 + 54*x^7 + 120*x^6 + 110*x^5 + 124*x^4 + 69*x^3 + 88*x^2 + 77*x + 62, x^27 + 33*x^25 + 86*x^24 + 86*x^23 + 120*x^22 + 78*x^21 + 12*x^20 + 83*x^19 + 88*x^18 + 27*x^17 + 42*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 10*x^8 + 6*x^7 + 24*x^6 + 94*x^5 + 12*x^4 + 53*x^3 + 56*x^2 + 29*x + 54, x^27 + 33*x^25 + 14*x^24 + 118*x^23 + 72*x^22 + 78*x^21 + 12*x^20 + 115*x^19 + 8*x^18 + 91*x^17 + 34*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 50*x^8 + 38*x^7 + 40*x^6 + 94*x^5 + 76*x^4 + 85*x^3 + 40*x^2 + 93*x + 94, x^27 + 33*x^25 + 58*x^24 + 86*x^23 + 8*x^22 + 78*x^21 + 84*x^20 + 83*x^19 + 40*x^18 + 27*x^17 + 6*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 102*x^8 + 6*x^7 + 104*x^6 + 94*x^5 + 84*x^4 + 53*x^3 + 72*x^2 + 29*x + 26, x^27 + 33*x^25 + 102*x^24 + 38*x^23 + 72*x^22 + 30*x^21 + 124*x^20 + 3*x^19 + 8*x^18 + 75*x^17 + 74*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 90*x^8 + 22*x^7 + 40*x^6 + 110*x^5 + 60*x^4 + 37*x^3 + 40*x^2 + 13*x + 54, x^27 + 33*x^25 + 74*x^24 + 102*x^23 + 56*x^22 + 94*x^21 + 36*x^20 + 67*x^19 + 120*x^18 + 11*x^17 + 70*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 118*x^8 + 86*x^7 + 88*x^6 + 46*x^5 + 100*x^4 + 101*x^3 + 88*x^2 + 77*x + 58, x^27 + 33*x^25 + 110*x^24 + 6*x^23 + 24*x^22 + 94*x^21 + 92*x^20 + 99*x^19 + 56*x^18 + 75*x^17 + 50*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 50*x^8 + 118*x^7 + 56*x^6 + 46*x^5 + 92*x^4 + 5*x^3 + 24*x^2 + 13*x + 110, x^27 + 33*x^25 + 54*x^24 + 118*x^23 + 56*x^22 + 110*x^21 + 12*x^20 + 51*x^19 + 24*x^18 + 123*x^17 + 10*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 42*x^8 + 38*x^7 + 88*x^6 + 126*x^5 + 12*x^4 + 21*x^3 + 120*x^2 + 125*x + 86, x^27 + 33*x^25 + 62*x^24 + 118*x^23 + 8*x^22 + 78*x^21 + 108*x^20 + 115*x^19 + 72*x^18 + 91*x^17 + 114*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 2*x^8 + 38*x^7 + 104*x^6 + 94*x^5 + 44*x^4 + 85*x^3 + 104*x^2 + 93*x + 14, x^27 + 33*x^25 + 6*x^24 + 118*x^23 + 24*x^22 + 46*x^21 + 12*x^20 + 51*x^19 + 56*x^18 + 59*x^17 + 90*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 26*x^8 + 38*x^7 + 56*x^6 + 62*x^5 + 12*x^4 + 21*x^3 + 24*x^2 + 61*x + 70, x^27 + 33*x^25 + 50*x^24 + 86*x^23 + 56*x^22 + 110*x^21 + 52*x^20 + 19*x^19 + 120*x^18 + 59*x^17 + 94*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 14*x^8 + 6*x^7 + 88*x^6 + 126*x^5 + 116*x^4 + 117*x^3 + 88*x^2 + 61*x + 34, x^27 + 33*x^25 + 86*x^24 + 54*x^23 + 24*x^22 + 110*x^21 + 108*x^20 + 115*x^19 + 56*x^18 + 123*x^17 + 74*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 74*x^8 + 102*x^7 + 56*x^6 + 126*x^5 + 108*x^4 + 85*x^3 + 24*x^2 + 125*x + 86, x^27 + 33*x^25 + 118*x^24 + 6*x^23 + 8*x^22 + 62*x^21 + 92*x^20 + 35*x^19 + 72*x^18 + 43*x^17 + 122*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 74*x^8 + 118*x^7 + 104*x^6 + 14*x^5 + 28*x^4 + 69*x^3 + 104*x^2 + 109*x + 6, x^27 + 33*x^25 + 2*x^24 + 118*x^23 + 88*x^22 + 14*x^21 + 52*x^20 + 115*x^19 + 88*x^18 + 27*x^17 + 46*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 126*x^8 + 38*x^7 + 120*x^6 + 30*x^5 + 116*x^4 + 85*x^3 + 56*x^2 + 29*x + 18, x^27 + 33*x^25 + 62*x^24 + 54*x^23 + 72*x^22 + 78*x^21 + 108*x^20 + 51*x^19 + 8*x^18 + 91*x^17 + 114*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 2*x^8 + 102*x^7 + 40*x^6 + 94*x^5 + 44*x^4 + 21*x^3 + 40*x^2 + 93*x + 14, x^27 + 33*x^25 + 122*x^24 + 70*x^23 + 120*x^22 + 126*x^21 + 68*x^20 + 99*x^19 + 56*x^18 + 107*x^17 + 86*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 70*x^8 + 54*x^7 + 24*x^6 + 78*x^5 + 4*x^4 + 5*x^3 + 24*x^2 + 45*x + 42, x^27 + 33*x^25 + 26*x^24 + 86*x^23 + 104*x^22 + 78*x^21 + 116*x^20 + 83*x^19 + 72*x^18 + 27*x^17 + 70*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 70*x^8 + 6*x^7 + 72*x^6 + 94*x^5 + 116*x^4 + 53*x^3 + 104*x^2 + 29*x + 26, x^27 + 33*x^25 + 126*x^24 + 6*x^23 + 56*x^22 + 94*x^21 + 92*x^20 + 99*x^19 + 24*x^18 + 75*x^17 + 66*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 98*x^8 + 118*x^7 + 88*x^6 + 46*x^5 + 92*x^4 + 5*x^3 + 120*x^2 + 13*x + 30, x^27 + 33*x^25 + 10*x^24 + 86*x^23 + 104*x^22 + 14*x^21 + 84*x^20 + 83*x^19 + 72*x^18 + 91*x^17 + 86*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 86*x^8 + 6*x^7 + 72*x^6 + 30*x^5 + 84*x^4 + 53*x^3 + 104*x^2 + 93*x + 10, x^27 + 33*x^25 + 114*x^24 + 102*x^23 + 72*x^22 + 62*x^21 + 68*x^20 + 3*x^19 + 104*x^18 + 107*x^17 + 14*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 46*x^8 + 86*x^7 + 40*x^6 + 14*x^5 + 68*x^4 + 37*x^3 + 8*x^2 + 45*x + 18, x^27 + 33*x^25 + 54*x^24 + 86*x^23 + 56*x^22 + 78*x^21 + 12*x^20 + 83*x^19 + 24*x^18 + 27*x^17 + 10*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 42*x^8 + 6*x^7 + 88*x^6 + 94*x^5 + 12*x^4 + 53*x^3 + 120*x^2 + 29*x + 86, x^27 + 33*x^25 + 50*x^24 + 86*x^23 + 24*x^22 + 46*x^21 + 84*x^20 + 19*x^19 + 24*x^18 + 123*x^17 + 62*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 78*x^8 + 6*x^7 + 56*x^6 + 62*x^5 + 20*x^4 + 117*x^3 + 120*x^2 + 125*x + 2, x^27 + 33*x^25 + 90*x^24 + 38*x^23 + 56*x^22 + 94*x^21 + 68*x^20 + 3*x^19 + 120*x^18 + 11*x^17 + 54*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 102*x^8 + 22*x^7 + 88*x^6 + 46*x^5 + 4*x^4 + 37*x^3 + 88*x^2 + 77*x + 74, x^27 + 33*x^25 + 114*x^24 + 70*x^23 + 40*x^22 + 94*x^21 + 100*x^20 + 35*x^19 + 8*x^18 + 75*x^17 + 110*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 110*x^8 + 54*x^7 + 8*x^6 + 46*x^5 + 100*x^4 + 69*x^3 + 40*x^2 + 13*x + 114, x^27 + 33*x^25 + 70*x^24 + 54*x^23 + 56*x^22 + 46*x^21 + 108*x^20 + 115*x^19 + 24*x^18 + 59*x^17 + 58*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 26*x^8 + 102*x^7 + 88*x^6 + 62*x^5 + 108*x^4 + 85*x^3 + 120*x^2 + 61*x + 38, x^27 + 33*x^25 + 14*x^24 + 70*x^23 + 24*x^22 + 94*x^21 + 92*x^20 + 35*x^19 + 56*x^18 + 75*x^17 + 82*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 18*x^8 + 54*x^7 + 56*x^6 + 46*x^5 + 92*x^4 + 69*x^3 + 24*x^2 + 13*x + 78, x^27 + 33*x^25 + 10*x^24 + 54*x^23 + 104*x^22 + 46*x^21 + 20*x^20 + 115*x^19 + 72*x^18 + 59*x^17 + 22*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 86*x^8 + 102*x^7 + 72*x^6 + 62*x^5 + 20*x^4 + 85*x^3 + 104*x^2 + 61*x + 74, x^27 + 33*x^25 + 74*x^24 + 70*x^23 + 24*x^22 + 126*x^21 + 68*x^20 + 99*x^19 + 24*x^18 + 107*x^17 + 38*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 54*x^8 + 54*x^7 + 56*x^6 + 78*x^5 + 4*x^4 + 5*x^3 + 120*x^2 + 45*x + 26, x^27 + 33*x^25 + 62*x^24 + 6*x^23 + 56*x^22 + 94*x^21 + 92*x^20 + 99*x^19 + 24*x^18 + 75*x^17 + 2*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 34*x^8 + 118*x^7 + 88*x^6 + 46*x^5 + 92*x^4 + 5*x^3 + 120*x^2 + 13*x + 94, x^27 + 33*x^25 + 22*x^24 + 6*x^23 + 104*x^22 + 126*x^21 + 60*x^20 + 35*x^19 + 104*x^18 + 107*x^17 + 58*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 106*x^8 + 118*x^7 + 72*x^6 + 78*x^5 + 124*x^4 + 69*x^3 + 8*x^2 + 45*x + 6, x^27 + 33*x^25 + 66*x^24 + 54*x^23 + 120*x^22 + 14*x^21 + 20*x^20 + 51*x^19 + 56*x^18 + 27*x^17 + 14*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 126*x^8 + 102*x^7 + 24*x^6 + 30*x^5 + 84*x^4 + 21*x^3 + 24*x^2 + 29*x + 114, x^27 + 33*x^25 + 2*x^24 + 54*x^23 + 56*x^22 + 14*x^21 + 84*x^20 + 51*x^19 + 120*x^18 + 27*x^17 + 14*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 62*x^8 + 102*x^7 + 88*x^6 + 30*x^5 + 20*x^4 + 21*x^3 + 88*x^2 + 29*x + 114, x^27 + 33*x^25 + 50*x^24 + 86*x^23 + 88*x^22 + 46*x^21 + 20*x^20 + 19*x^19 + 88*x^18 + 123*x^17 + 126*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 78*x^8 + 6*x^7 + 120*x^6 + 62*x^5 + 84*x^4 + 117*x^3 + 56*x^2 + 125*x + 66, x^27 + 33*x^25 + 90*x^24 + 70*x^23 + 88*x^22 + 126*x^21 + 100*x^20 + 99*x^19 + 88*x^18 + 107*x^17 + 22*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 38*x^8 + 54*x^7 + 120*x^6 + 78*x^5 + 36*x^4 + 5*x^3 + 56*x^2 + 45*x + 42, x^27 + 33*x^25 + 98*x^24 + 38*x^23 + 40*x^22 + 62*x^21 + 4*x^20 + 67*x^19 + 8*x^18 + 107*x^17 + 62*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 126*x^8 + 22*x^7 + 8*x^6 + 14*x^5 + 4*x^4 + 101*x^3 + 40*x^2 + 45*x + 34, x^27 + 33*x^25 + 106*x^24 + 102*x^23 + 56*x^22 + 94*x^21 + 100*x^20 + 67*x^19 + 120*x^18 + 11*x^17 + 38*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 86*x^8 + 86*x^7 + 88*x^6 + 46*x^5 + 36*x^4 + 101*x^3 + 88*x^2 + 77*x + 90, x^27 + 33*x^25 + 86*x^24 + 38*x^23 + 40*x^22 + 94*x^21 + 60*x^20 + 3*x^19 + 40*x^18 + 11*x^17 + 122*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 42*x^8 + 22*x^7 + 8*x^6 + 46*x^5 + 124*x^4 + 37*x^3 + 72*x^2 + 77*x + 70, x^27 + 33*x^25 + 66*x^24 + 70*x^23 + 40*x^22 + 30*x^21 + 4*x^20 + 35*x^19 + 8*x^18 + 11*x^17 + 30*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 30*x^8 + 54*x^7 + 8*x^6 + 110*x^5 + 4*x^4 + 69*x^3 + 40*x^2 + 77*x + 66, x^27 + 33*x^25 + 78*x^24 + 54*x^23 + 104*x^22 + 14*x^21 + 44*x^20 + 51*x^19 + 104*x^18 + 27*x^17 + 66*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 50*x^8 + 102*x^7 + 72*x^6 + 30*x^5 + 108*x^4 + 21*x^3 + 8*x^2 + 29*x + 126, x^27 + 33*x^25 + 62*x^24 + 54*x^23 + 72*x^22 + 14*x^21 + 44*x^20 + 51*x^19 + 8*x^18 + 27*x^17 + 50*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 2*x^8 + 102*x^7 + 40*x^6 + 30*x^5 + 108*x^4 + 21*x^3 + 40*x^2 + 29*x + 78, x^27 + 33*x^25 + 42*x^24 + 86*x^23 + 40*x^22 + 14*x^21 + 84*x^20 + 83*x^19 + 8*x^18 + 91*x^17 + 118*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 54*x^8 + 6*x^7 + 8*x^6 + 30*x^5 + 84*x^4 + 53*x^3 + 40*x^2 + 93*x + 106, x^27 + 33*x^25 + 102*x^24 + 102*x^23 + 104*x^22 + 94*x^21 + 28*x^20 + 67*x^19 + 104*x^18 + 11*x^17 + 42*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 26*x^8 + 86*x^7 + 72*x^6 + 46*x^5 + 92*x^4 + 101*x^3 + 8*x^2 + 77*x + 22, x^27 + 33*x^25 + 14*x^24 + 38*x^23 + 56*x^22 + 126*x^21 + 60*x^20 + 67*x^19 + 24*x^18 + 43*x^17 + 114*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 82*x^8 + 22*x^7 + 88*x^6 + 78*x^5 + 60*x^4 + 101*x^3 + 120*x^2 + 109*x + 110, x^27 + 33*x^25 + 114*x^24 + 6*x^23 + 72*x^22 + 94*x^21 + 68*x^20 + 99*x^19 + 104*x^18 + 75*x^17 + 14*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 46*x^8 + 118*x^7 + 40*x^6 + 46*x^5 + 68*x^4 + 5*x^3 + 8*x^2 + 13*x + 18, x^27 + 33*x^25 + 6*x^24 + 38*x^23 + 72*x^22 + 94*x^21 + 124*x^20 + 3*x^19 + 8*x^18 + 11*x^17 + 106*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 58*x^8 + 22*x^7 + 40*x^6 + 46*x^5 + 60*x^4 + 37*x^3 + 40*x^2 + 77*x + 22, x^27 + 33*x^25 + 118*x^24 + 70*x^23 + 8*x^22 + 126*x^21 + 92*x^20 + 99*x^19 + 72*x^18 + 107*x^17 + 122*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 74*x^8 + 54*x^7 + 104*x^6 + 78*x^5 + 28*x^4 + 5*x^3 + 104*x^2 + 45*x + 6, x^27 + 33*x^25 + 114*x^24 + 22*x^23 + 88*x^22 + 46*x^21 + 84*x^20 + 83*x^19 + 88*x^18 + 123*x^17 + 126*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 14*x^8 + 70*x^7 + 120*x^6 + 62*x^5 + 20*x^4 + 53*x^3 + 56*x^2 + 125*x + 66, x^27 + 33*x^25 + 126*x^24 + 54*x^23 + 72*x^22 + 14*x^21 + 44*x^20 + 51*x^19 + 8*x^18 + 27*x^17 + 114*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 66*x^8 + 102*x^7 + 40*x^6 + 30*x^5 + 108*x^4 + 21*x^3 + 40*x^2 + 29*x + 14, x^27 + 33*x^25 + 2*x^24 + 70*x^23 + 8*x^22 + 30*x^21 + 100*x^20 + 35*x^19 + 40*x^18 + 11*x^17 + 126*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 30*x^8 + 54*x^7 + 104*x^6 + 110*x^5 + 100*x^4 + 69*x^3 + 72*x^2 + 77*x + 34, x^27 + 33*x^25 + 50*x^24 + 38*x^23 + 72*x^22 + 126*x^21 + 68*x^20 + 67*x^19 + 104*x^18 + 43*x^17 + 78*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 110*x^8 + 22*x^7 + 40*x^6 + 78*x^5 + 68*x^4 + 101*x^3 + 8*x^2 + 109*x + 82, x^27 + 33*x^25 + 14*x^24 + 86*x^23 + 72*x^22 + 110*x^21 + 76*x^20 + 19*x^19 + 8*x^18 + 59*x^17 + 98*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 50*x^8 + 6*x^7 + 40*x^6 + 126*x^5 + 12*x^4 + 117*x^3 + 40*x^2 + 61*x + 30, x^27 + 33*x^25 + 50*x^24 + 102*x^23 + 72*x^22 + 62*x^21 + 68*x^20 + 3*x^19 + 104*x^18 + 107*x^17 + 78*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 110*x^8 + 86*x^7 + 40*x^6 + 14*x^5 + 68*x^4 + 37*x^3 + 8*x^2 + 45*x + 82, x^27 + 33*x^25 + 30*x^24 + 70*x^23 + 120*x^22 + 30*x^21 + 92*x^20 + 35*x^19 + 88*x^18 + 11*x^17 + 98*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 66*x^8 + 54*x^7 + 24*x^6 + 110*x^5 + 92*x^4 + 69*x^3 + 56*x^2 + 77*x + 126, x^27 + 33*x^25 + 2*x^24 + 86*x^23 + 56*x^22 + 46*x^21 + 84*x^20 + 19*x^19 + 120*x^18 + 123*x^17 + 14*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 62*x^8 + 6*x^7 + 88*x^6 + 62*x^5 + 20*x^4 + 117*x^3 + 88*x^2 + 125*x + 114, x^27 + 33*x^25 + 126*x^24 + 118*x^23 + 8*x^22 + 78*x^21 + 108*x^20 + 115*x^19 + 72*x^18 + 91*x^17 + 50*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 66*x^8 + 38*x^7 + 104*x^6 + 94*x^5 + 44*x^4 + 85*x^3 + 104*x^2 + 93*x + 78, x^27 + 33*x^25 + 66*x^24 + 102*x^23 + 104*x^22 + 62*x^21 + 68*x^20 + 3*x^19 + 72*x^18 + 107*x^17 + 94*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 30*x^8 + 86*x^7 + 72*x^6 + 14*x^5 + 68*x^4 + 37*x^3 + 104*x^2 + 45*x + 2, x^27 + 33*x^25 + 82*x^24 + 54*x^23 + 24*x^22 + 14*x^21 + 20*x^20 + 51*x^19 + 24*x^18 + 27*x^17 + 30*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 46*x^8 + 102*x^7 + 56*x^6 + 30*x^5 + 84*x^4 + 21*x^3 + 120*x^2 + 29*x + 34, x^27 + 33*x^25 + 90*x^24 + 38*x^23 + 88*x^22 + 30*x^21 + 36*x^20 + 3*x^19 + 88*x^18 + 75*x^17 + 86*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 38*x^8 + 22*x^7 + 120*x^6 + 110*x^5 + 100*x^4 + 37*x^3 + 56*x^2 + 13*x + 106, x^27 + 33*x^25 + 46*x^24 + 54*x^23 + 72*x^22 + 14*x^21 + 76*x^20 + 51*x^19 + 8*x^18 + 27*x^17 + 2*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 18*x^8 + 102*x^7 + 40*x^6 + 30*x^5 + 12*x^4 + 21*x^3 + 40*x^2 + 29*x + 126, x^27 + 33*x^25 + 62*x^24 + 6*x^23 + 120*x^22 + 94*x^21 + 28*x^20 + 99*x^19 + 88*x^18 + 75*x^17 + 66*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 34*x^8 + 118*x^7 + 24*x^6 + 46*x^5 + 28*x^4 + 5*x^3 + 56*x^2 + 13*x + 30, x^27 + 33*x^25 + 110*x^24 + 38*x^23 + 88*x^22 + 62*x^21 + 92*x^20 + 67*x^19 + 120*x^18 + 107*x^17 + 50*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 50*x^8 + 22*x^7 + 120*x^6 + 14*x^5 + 92*x^4 + 101*x^3 + 88*x^2 + 45*x + 110, x^27 + 33*x^25 + 122*x^24 + 102*x^23 + 88*x^22 + 30*x^21 + 36*x^20 + 67*x^19 + 88*x^18 + 75*x^17 + 118*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 6*x^8 + 86*x^7 + 120*x^6 + 110*x^5 + 100*x^4 + 101*x^3 + 56*x^2 + 13*x + 74, x^27 + 33*x^25 + 66*x^24 + 22*x^23 + 88*x^22 + 46*x^21 + 52*x^20 + 83*x^19 + 88*x^18 + 123*x^17 + 110*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 62*x^8 + 70*x^7 + 120*x^6 + 62*x^5 + 116*x^4 + 53*x^3 + 56*x^2 + 125*x + 82, x^27 + 33*x^25 + 66*x^24 + 70*x^23 + 8*x^22 + 30*x^21 + 100*x^20 + 35*x^19 + 40*x^18 + 11*x^17 + 62*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 94*x^8 + 54*x^7 + 104*x^6 + 110*x^5 + 100*x^4 + 69*x^3 + 72*x^2 + 77*x + 98, x^27 + 33*x^25 + 22*x^24 + 118*x^23 + 56*x^22 + 110*x^21 + 76*x^20 + 51*x^19 + 24*x^18 + 123*x^17 + 42*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 74*x^8 + 38*x^7 + 88*x^6 + 126*x^5 + 76*x^4 + 21*x^3 + 120*x^2 + 125*x + 54, x^27 + 33*x^25 + 78*x^24 + 86*x^23 + 40*x^22 + 110*x^21 + 44*x^20 + 19*x^19 + 40*x^18 + 59*x^17 + 66*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 50*x^8 + 6*x^7 + 8*x^6 + 126*x^5 + 108*x^4 + 117*x^3 + 72*x^2 + 61*x + 126, x^27 + 33*x^25 + 30*x^24 + 54*x^23 + 72*x^22 + 14*x^21 + 108*x^20 + 51*x^19 + 8*x^18 + 27*x^17 + 82*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 34*x^8 + 102*x^7 + 40*x^6 + 30*x^5 + 44*x^4 + 21*x^3 + 40*x^2 + 29*x + 46, x^27 + 33*x^25 + 110*x^24 + 38*x^23 + 24*x^22 + 126*x^21 + 92*x^20 + 67*x^19 + 56*x^18 + 43*x^17 + 50*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 50*x^8 + 22*x^7 + 56*x^6 + 78*x^5 + 92*x^4 + 101*x^3 + 24*x^2 + 109*x + 110, x^27 + 33*x^25 + 114*x^24 + 38*x^23 + 104*x^22 + 62*x^21 + 36*x^20 + 67*x^19 + 72*x^18 + 107*x^17 + 46*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 110*x^8 + 22*x^7 + 72*x^6 + 14*x^5 + 36*x^4 + 101*x^3 + 104*x^2 + 45*x + 50, x^27 + 33*x^25 + 102*x^24 + 22*x^23 + 24*x^22 + 78*x^21 + 76*x^20 + 19*x^19 + 56*x^18 + 27*x^17 + 122*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 58*x^8 + 70*x^7 + 56*x^6 + 94*x^5 + 76*x^4 + 117*x^3 + 24*x^2 + 29*x + 38, x^27 + 33*x^25 + 118*x^24 + 86*x^23 + 56*x^22 + 78*x^21 + 12*x^20 + 83*x^19 + 24*x^18 + 27*x^17 + 74*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 106*x^8 + 6*x^7 + 88*x^6 + 94*x^5 + 12*x^4 + 53*x^3 + 120*x^2 + 29*x + 22, x^27 + 33*x^25 + 50*x^24 + 118*x^23 + 24*x^22 + 14*x^21 + 20*x^20 + 115*x^19 + 24*x^18 + 27*x^17 + 126*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 78*x^8 + 38*x^7 + 56*x^6 + 30*x^5 + 84*x^4 + 85*x^3 + 120*x^2 + 29*x + 66, x^27 + 33*x^25 + 90*x^24 + 54*x^23 + 40*x^22 + 110*x^21 + 116*x^20 + 115*x^19 + 8*x^18 + 123*x^17 + 6*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 6*x^8 + 102*x^7 + 8*x^6 + 126*x^5 + 116*x^4 + 85*x^3 + 40*x^2 + 125*x + 90, x^27 + 33*x^25 + 22*x^24 + 54*x^23 + 88*x^22 + 110*x^21 + 44*x^20 + 115*x^19 + 120*x^18 + 123*x^17 + 74*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 10*x^8 + 102*x^7 + 120*x^6 + 126*x^5 + 44*x^4 + 85*x^3 + 88*x^2 + 125*x + 86, x^27 + 33*x^25 + 38*x^24 + 6*x^23 + 8*x^22 + 126*x^21 + 60*x^20 + 35*x^19 + 72*x^18 + 107*x^17 + 74*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 26*x^8 + 118*x^7 + 104*x^6 + 78*x^5 + 124*x^4 + 69*x^3 + 104*x^2 + 45*x + 54, x^27 + 33*x^25 + 126*x^24 + 102*x^23 + 56*x^22 + 62*x^21 + 92*x^20 + 3*x^19 + 24*x^18 + 107*x^17 + 66*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 98*x^8 + 86*x^7 + 88*x^6 + 14*x^5 + 92*x^4 + 37*x^3 + 120*x^2 + 45*x + 30, x^27 + 33*x^25 + 10*x^24 + 118*x^23 + 72*x^22 + 46*x^21 + 52*x^20 + 51*x^19 + 104*x^18 + 59*x^17 + 118*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 22*x^8 + 38*x^7 + 40*x^6 + 62*x^5 + 52*x^4 + 21*x^3 + 8*x^2 + 61*x + 42, x^27 + 33*x^25 + 110*x^24 + 6*x^23 + 88*x^22 + 94*x^21 + 28*x^20 + 99*x^19 + 120*x^18 + 75*x^17 + 114*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 50*x^8 + 118*x^7 + 120*x^6 + 46*x^5 + 28*x^4 + 5*x^3 + 88*x^2 + 13*x + 46, x^27 + 33*x^25 + 34*x^24 + 6*x^23 + 104*x^22 + 94*x^21 + 4*x^20 + 99*x^19 + 72*x^18 + 75*x^17 + 126*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 62*x^8 + 118*x^7 + 72*x^6 + 46*x^5 + 4*x^4 + 5*x^3 + 104*x^2 + 13*x + 98, x^27 + 33*x^25 + 14*x^24 + 6*x^23 + 56*x^22 + 30*x^21 + 124*x^20 + 99*x^19 + 24*x^18 + 11*x^17 + 50*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 82*x^8 + 118*x^7 + 88*x^6 + 110*x^5 + 124*x^4 + 5*x^3 + 120*x^2 + 77*x + 46, x^27 + 33*x^25 + 90*x^24 + 102*x^23 + 24*x^22 + 30*x^21 + 36*x^20 + 67*x^19 + 24*x^18 + 75*x^17 + 86*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 38*x^8 + 86*x^7 + 56*x^6 + 110*x^5 + 100*x^4 + 101*x^3 + 120*x^2 + 13*x + 106, x^27 + 33*x^25 + 82*x^24 + 86*x^23 + 24*x^22 + 46*x^21 + 20*x^20 + 19*x^19 + 24*x^18 + 123*x^17 + 30*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 46*x^8 + 6*x^7 + 56*x^6 + 62*x^5 + 84*x^4 + 117*x^3 + 120*x^2 + 125*x + 34, x^27 + 33*x^25 + 126*x^24 + 70*x^23 + 24*x^22 + 94*x^21 + 124*x^20 + 35*x^19 + 56*x^18 + 75*x^17 + 34*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 34*x^8 + 54*x^7 + 56*x^6 + 46*x^5 + 124*x^4 + 69*x^3 + 24*x^2 + 13*x + 126, x^27 + 33*x^25 + 58*x^24 + 54*x^23 + 40*x^22 + 110*x^21 + 52*x^20 + 115*x^19 + 8*x^18 + 123*x^17 + 38*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 38*x^8 + 102*x^7 + 8*x^6 + 126*x^5 + 52*x^4 + 85*x^3 + 40*x^2 + 125*x + 58, x^27 + 33*x^25 + 62*x^24 + 38*x^23 + 56*x^22 + 126*x^21 + 92*x^20 + 67*x^19 + 24*x^18 + 43*x^17 + 2*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 34*x^8 + 22*x^7 + 88*x^6 + 78*x^5 + 92*x^4 + 101*x^3 + 120*x^2 + 109*x + 94, x^27 + 33*x^25 + 94*x^24 + 22*x^23 + 104*x^22 + 46*x^21 + 76*x^20 + 83*x^19 + 104*x^18 + 123*x^17 + 50*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 34*x^8 + 70*x^7 + 72*x^6 + 62*x^5 + 12*x^4 + 53*x^3 + 8*x^2 + 125*x + 14, x^27 + 33*x^25 + 66*x^24 + 102*x^23 + 72*x^22 + 126*x^21 + 100*x^20 + 3*x^19 + 104*x^18 + 43*x^17 + 62*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 94*x^8 + 86*x^7 + 40*x^6 + 78*x^5 + 100*x^4 + 37*x^3 + 8*x^2 + 109*x + 98, x^27 + 33*x^25 + 66*x^24 + 54*x^23 + 88*x^22 + 78*x^21 + 52*x^20 + 51*x^19 + 88*x^18 + 91*x^17 + 110*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 62*x^8 + 102*x^7 + 120*x^6 + 94*x^5 + 116*x^4 + 21*x^3 + 56*x^2 + 93*x + 82, x^27 + 33*x^25 + 66*x^24 + 118*x^23 + 24*x^22 + 78*x^21 + 52*x^20 + 115*x^19 + 24*x^18 + 91*x^17 + 110*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 62*x^8 + 38*x^7 + 56*x^6 + 94*x^5 + 116*x^4 + 85*x^3 + 120*x^2 + 93*x + 82, x^27 + 33*x^25 + 42*x^24 + 22*x^23 + 72*x^22 + 14*x^21 + 52*x^20 + 19*x^19 + 104*x^18 + 91*x^17 + 22*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 118*x^8 + 70*x^7 + 40*x^6 + 30*x^5 + 52*x^4 + 117*x^3 + 8*x^2 + 93*x + 10, x^27 + 33*x^25 + 70*x^24 + 6*x^23 + 72*x^22 + 62*x^21 + 124*x^20 + 35*x^19 + 8*x^18 + 43*x^17 + 42*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 122*x^8 + 118*x^7 + 40*x^6 + 14*x^5 + 60*x^4 + 69*x^3 + 40*x^2 + 109*x + 86, x^27 + 33*x^25 + 86*x^24 + 38*x^23 + 8*x^22 + 30*x^21 + 92*x^20 + 3*x^19 + 72*x^18 + 75*x^17 + 90*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 106*x^8 + 22*x^7 + 104*x^6 + 110*x^5 + 28*x^4 + 37*x^3 + 104*x^2 + 13*x + 38, x^27 + 33*x^25 + 118*x^24 + 54*x^23 + 88*x^22 + 46*x^21 + 44*x^20 + 115*x^19 + 120*x^18 + 59*x^17 + 42*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 42*x^8 + 102*x^7 + 120*x^6 + 62*x^5 + 44*x^4 + 85*x^3 + 88*x^2 + 61*x + 118, x^27 + 33*x^25 + 78*x^24 + 86*x^23 + 8*x^22 + 110*x^21 + 12*x^20 + 19*x^19 + 72*x^18 + 59*x^17 + 98*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 114*x^8 + 6*x^7 + 104*x^6 + 126*x^5 + 76*x^4 + 117*x^3 + 104*x^2 + 61*x + 30, x^27 + 33*x^25 + 62*x^24 + 22*x^23 + 72*x^22 + 110*x^21 + 44*x^20 + 83*x^19 + 8*x^18 + 59*x^17 + 50*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 2*x^8 + 70*x^7 + 40*x^6 + 126*x^5 + 108*x^4 + 53*x^3 + 40*x^2 + 61*x + 78, x^27 + 33*x^25 + 122*x^24 + 118*x^23 + 72*x^22 + 110*x^21 + 20*x^20 + 51*x^19 + 104*x^18 + 123*x^17 + 6*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 38*x^8 + 38*x^7 + 40*x^6 + 126*x^5 + 20*x^4 + 21*x^3 + 8*x^2 + 125*x + 26, x^27 + 33*x^25 + 6*x^24 + 102*x^23 + 104*x^22 + 94*x^21 + 92*x^20 + 67*x^19 + 104*x^18 + 11*x^17 + 10*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 122*x^8 + 86*x^7 + 72*x^6 + 46*x^5 + 28*x^4 + 101*x^3 + 8*x^2 + 77*x + 54, x^27 + 33*x^25 + 90*x^24 + 118*x^23 + 72*x^22 + 46*x^21 + 20*x^20 + 51*x^19 + 104*x^18 + 59*x^17 + 102*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 70*x^8 + 38*x^7 + 40*x^6 + 62*x^5 + 20*x^4 + 21*x^3 + 8*x^2 + 61*x + 58, x^27 + 33*x^25 + 94*x^24 + 102*x^23 + 88*x^22 + 62*x^21 + 60*x^20 + 3*x^19 + 120*x^18 + 107*x^17 + 66*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 66*x^8 + 86*x^7 + 120*x^6 + 14*x^5 + 60*x^4 + 37*x^3 + 88*x^2 + 45*x + 94, x^27 + 33*x^25 + 14*x^24 + 38*x^23 + 88*x^22 + 62*x^21 + 28*x^20 + 67*x^19 + 120*x^18 + 107*x^17 + 18*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 18*x^8 + 22*x^7 + 120*x^6 + 14*x^5 + 28*x^4 + 101*x^3 + 88*x^2 + 45*x + 14, x^27 + 33*x^25 + 50*x^24 + 86*x^23 + 120*x^22 + 110*x^21 + 116*x^20 + 19*x^19 + 56*x^18 + 59*x^17 + 30*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 14*x^8 + 6*x^7 + 24*x^6 + 126*x^5 + 52*x^4 + 117*x^3 + 24*x^2 + 61*x + 98, x^27 + 33*x^25 + 22*x^24 + 38*x^23 + 8*x^22 + 94*x^21 + 28*x^20 + 3*x^19 + 72*x^18 + 11*x^17 + 90*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 42*x^8 + 22*x^7 + 104*x^6 + 46*x^5 + 92*x^4 + 37*x^3 + 104*x^2 + 77*x + 38, x^27 + 33*x^25 + 2*x^24 + 70*x^23 + 104*x^22 + 30*x^21 + 68*x^20 + 35*x^19 + 72*x^18 + 11*x^17 + 30*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 94*x^8 + 54*x^7 + 72*x^6 + 110*x^5 + 68*x^4 + 69*x^3 + 104*x^2 + 77*x + 66, x^27 + 33*x^25 + 110*x^24 + 118*x^23 + 72*x^22 + 14*x^21 + 12*x^20 + 115*x^19 + 8*x^18 + 27*x^17 + 2*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 82*x^8 + 38*x^7 + 40*x^6 + 30*x^5 + 76*x^4 + 85*x^3 + 40*x^2 + 29*x + 126, x^27 + 33*x^25 + 66*x^24 + 102*x^23 + 8*x^22 + 126*x^21 + 36*x^20 + 3*x^19 + 40*x^18 + 43*x^17 + 126*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 94*x^8 + 86*x^7 + 104*x^6 + 78*x^5 + 36*x^4 + 37*x^3 + 72*x^2 + 109*x + 34, x^27 + 33*x^25 + 90*x^24 + 38*x^23 + 120*x^22 + 30*x^21 + 68*x^20 + 3*x^19 + 56*x^18 + 75*x^17 + 54*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 102*x^8 + 22*x^7 + 24*x^6 + 110*x^5 + 4*x^4 + 37*x^3 + 24*x^2 + 13*x + 74, x^27 + 33*x^25 + 78*x^24 + 22*x^23 + 104*x^22 + 110*x^21 + 44*x^20 + 83*x^19 + 104*x^18 + 59*x^17 + 66*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 50*x^8 + 70*x^7 + 72*x^6 + 126*x^5 + 108*x^4 + 53*x^3 + 8*x^2 + 61*x + 126, x^27 + 33*x^25 + 98*x^24 + 118*x^23 + 120*x^22 + 78*x^21 + 84*x^20 + 115*x^19 + 56*x^18 + 91*x^17 + 110*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 94*x^8 + 38*x^7 + 24*x^6 + 94*x^5 + 20*x^4 + 85*x^3 + 24*x^2 + 93*x + 18, x^27 + 33*x^25 + 50*x^24 + 38*x^23 + 40*x^22 + 126*x^21 + 36*x^20 + 67*x^19 + 8*x^18 + 43*x^17 + 110*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 46*x^8 + 22*x^7 + 8*x^6 + 78*x^5 + 36*x^4 + 101*x^3 + 40*x^2 + 109*x + 114, x^27 + 33*x^25 + 86*x^24 + 70*x^23 + 72*x^22 + 126*x^21 + 92*x^20 + 99*x^19 + 8*x^18 + 107*x^17 + 90*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 106*x^8 + 54*x^7 + 40*x^6 + 78*x^5 + 28*x^4 + 5*x^3 + 40*x^2 + 45*x + 38, x^27 + 33*x^25 + 62*x^24 + 102*x^23 + 88*x^22 + 126*x^21 + 60*x^20 + 3*x^19 + 120*x^18 + 43*x^17 + 34*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 98*x^8 + 86*x^7 + 120*x^6 + 78*x^5 + 60*x^4 + 37*x^3 + 88*x^2 + 109*x + 126, x^27 + 33*x^25 + 98*x^24 + 118*x^23 + 56*x^22 + 14*x^21 + 84*x^20 + 115*x^19 + 120*x^18 + 27*x^17 + 110*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 94*x^8 + 38*x^7 + 88*x^6 + 30*x^5 + 20*x^4 + 85*x^3 + 88*x^2 + 29*x + 18, x^27 + 33*x^25 + 94*x^24 + 38*x^23 + 56*x^22 + 126*x^21 + 28*x^20 + 67*x^19 + 24*x^18 + 43*x^17 + 98*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 2*x^8 + 22*x^7 + 88*x^6 + 78*x^5 + 28*x^4 + 101*x^3 + 120*x^2 + 109*x + 126, x^27 + 33*x^25 + 14*x^24 + 102*x^23 + 56*x^22 + 62*x^21 + 60*x^20 + 3*x^19 + 24*x^18 + 107*x^17 + 114*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 82*x^8 + 86*x^7 + 88*x^6 + 14*x^5 + 60*x^4 + 37*x^3 + 120*x^2 + 45*x + 110, x^27 + 33*x^25 + 34*x^24 + 54*x^23 + 24*x^22 + 78*x^21 + 52*x^20 + 51*x^19 + 24*x^18 + 91*x^17 + 78*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 94*x^8 + 102*x^7 + 56*x^6 + 94*x^5 + 116*x^4 + 21*x^3 + 120*x^2 + 93*x + 114, x^27 + 33*x^25 + 94*x^24 + 102*x^23 + 88*x^22 + 126*x^21 + 124*x^20 + 3*x^19 + 120*x^18 + 43*x^17 + 2*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 66*x^8 + 86*x^7 + 120*x^6 + 78*x^5 + 124*x^4 + 37*x^3 + 88*x^2 + 109*x + 30, x^27 + 33*x^25 + 70*x^24 + 86*x^23 + 120*x^22 + 14*x^21 + 108*x^20 + 83*x^19 + 88*x^18 + 91*x^17 + 58*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 26*x^8 + 6*x^7 + 24*x^6 + 30*x^5 + 108*x^4 + 53*x^3 + 56*x^2 + 93*x + 38, x^27 + 33*x^25 + 22*x^24 + 6*x^23 + 72*x^22 + 126*x^21 + 28*x^20 + 35*x^19 + 8*x^18 + 107*x^17 + 90*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 42*x^8 + 118*x^7 + 40*x^6 + 78*x^5 + 92*x^4 + 69*x^3 + 40*x^2 + 45*x + 38, x^27 + 33*x^25 + 126*x^24 + 6*x^23 + 24*x^22 + 94*x^21 + 60*x^20 + 99*x^19 + 56*x^18 + 75*x^17 + 98*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 34*x^8 + 118*x^7 + 56*x^6 + 46*x^5 + 60*x^4 + 5*x^3 + 24*x^2 + 13*x + 62, x^27 + 33*x^25 + 110*x^24 + 22*x^23 + 72*x^22 + 46*x^21 + 12*x^20 + 83*x^19 + 8*x^18 + 123*x^17 + 2*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 82*x^8 + 70*x^7 + 40*x^6 + 62*x^5 + 76*x^4 + 53*x^3 + 40*x^2 + 125*x + 126, x^27 + 33*x^25 + 114*x^24 + 38*x^23 + 40*x^22 + 62*x^21 + 100*x^20 + 67*x^19 + 8*x^18 + 107*x^17 + 110*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 110*x^8 + 22*x^7 + 8*x^6 + 14*x^5 + 100*x^4 + 101*x^3 + 40*x^2 + 45*x + 114, x^27 + 33*x^25 + 10*x^24 + 6*x^23 + 88*x^22 + 126*x^21 + 68*x^20 + 35*x^19 + 88*x^18 + 107*x^17 + 102*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 118*x^8 + 118*x^7 + 120*x^6 + 78*x^5 + 4*x^4 + 69*x^3 + 56*x^2 + 45*x + 90, x^27 + 33*x^25 + 118*x^24 + 118*x^23 + 120*x^22 + 110*x^21 + 76*x^20 + 51*x^19 + 88*x^18 + 123*x^17 + 10*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 106*x^8 + 38*x^7 + 24*x^6 + 126*x^5 + 76*x^4 + 21*x^3 + 56*x^2 + 125*x + 86, x^27 + 33*x^25 + 46*x^24 + 86*x^23 + 72*x^22 + 46*x^21 + 76*x^20 + 19*x^19 + 8*x^18 + 123*x^17 + 2*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 18*x^8 + 6*x^7 + 40*x^6 + 62*x^5 + 12*x^4 + 117*x^3 + 40*x^2 + 125*x + 126, x^27 + 33*x^25 + 110*x^24 + 6*x^23 + 56*x^22 + 94*x^21 + 124*x^20 + 99*x^19 + 24*x^18 + 75*x^17 + 18*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 114*x^8 + 118*x^7 + 88*x^6 + 46*x^5 + 124*x^4 + 5*x^3 + 120*x^2 + 13*x + 78, x^27 + 33*x^25 + 98*x^24 + 70*x^23 + 40*x^22 + 94*x^21 + 4*x^20 + 35*x^19 + 8*x^18 + 75*x^17 + 62*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 126*x^8 + 54*x^7 + 8*x^6 + 46*x^5 + 4*x^4 + 69*x^3 + 40*x^2 + 13*x + 34, x^27 + 33*x^25 + 86*x^24 + 86*x^23 + 88*x^22 + 14*x^21 + 44*x^20 + 83*x^19 + 120*x^18 + 91*x^17 + 10*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 74*x^8 + 6*x^7 + 120*x^6 + 30*x^5 + 44*x^4 + 53*x^3 + 88*x^2 + 93*x + 22, x^27 + 33*x^25 + 42*x^24 + 38*x^23 + 120*x^22 + 94*x^21 + 100*x^20 + 3*x^19 + 56*x^18 + 11*x^17 + 102*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 22*x^8 + 22*x^7 + 24*x^6 + 46*x^5 + 36*x^4 + 37*x^3 + 24*x^2 + 77*x + 26, x^27 + 33*x^25 + 66*x^24 + 70*x^23 + 104*x^22 + 30*x^21 + 68*x^20 + 35*x^19 + 72*x^18 + 11*x^17 + 94*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 30*x^8 + 54*x^7 + 72*x^6 + 110*x^5 + 68*x^4 + 69*x^3 + 104*x^2 + 77*x + 2, x^27 + 33*x^25 + 90*x^24 + 86*x^23 + 104*x^22 + 78*x^21 + 116*x^20 + 83*x^19 + 72*x^18 + 27*x^17 + 6*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 6*x^8 + 6*x^7 + 72*x^6 + 94*x^5 + 116*x^4 + 53*x^3 + 104*x^2 + 29*x + 90, x^27 + 33*x^25 + 58*x^24 + 70*x^23 + 120*x^22 + 126*x^21 + 68*x^20 + 99*x^19 + 56*x^18 + 107*x^17 + 22*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 6*x^8 + 54*x^7 + 24*x^6 + 78*x^5 + 4*x^4 + 5*x^3 + 24*x^2 + 45*x + 106, x^27 + 33*x^25 + 126*x^24 + 38*x^23 + 120*x^22 + 126*x^21 + 28*x^20 + 67*x^19 + 88*x^18 + 43*x^17 + 2*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 98*x^8 + 22*x^7 + 24*x^6 + 78*x^5 + 28*x^4 + 101*x^3 + 56*x^2 + 109*x + 94, x^27 + 33*x^25 + 38*x^24 + 86*x^23 + 56*x^22 + 78*x^21 + 44*x^20 + 83*x^19 + 24*x^18 + 27*x^17 + 90*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 58*x^8 + 6*x^7 + 88*x^6 + 94*x^5 + 44*x^4 + 53*x^3 + 120*x^2 + 29*x + 6, x^27 + 33*x^25 + 66*x^24 + 6*x^23 + 104*x^22 + 30*x^21 + 4*x^20 + 99*x^19 + 72*x^18 + 11*x^17 + 30*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 30*x^8 + 118*x^7 + 72*x^6 + 110*x^5 + 4*x^4 + 5*x^3 + 104*x^2 + 77*x + 66, x^27 + 33*x^25 + 70*x^24 + 38*x^23 + 8*x^22 + 30*x^21 + 124*x^20 + 3*x^19 + 72*x^18 + 75*x^17 + 42*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 122*x^8 + 22*x^7 + 104*x^6 + 110*x^5 + 60*x^4 + 37*x^3 + 104*x^2 + 13*x + 86, x^27 + 33*x^25 + 126*x^24 + 6*x^23 + 88*x^22 + 30*x^21 + 60*x^20 + 99*x^19 + 120*x^18 + 11*x^17 + 98*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 34*x^8 + 118*x^7 + 120*x^6 + 110*x^5 + 60*x^4 + 5*x^3 + 88*x^2 + 77*x + 62, x^27 + 33*x^25 + 94*x^24 + 118*x^23 + 8*x^22 + 78*x^21 + 44*x^20 + 115*x^19 + 72*x^18 + 91*x^17 + 82*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 98*x^8 + 38*x^7 + 104*x^6 + 94*x^5 + 108*x^4 + 85*x^3 + 104*x^2 + 93*x + 46, x^27 + 33*x^25 + 74*x^24 + 102*x^23 + 120*x^22 + 94*x^21 + 100*x^20 + 67*x^19 + 56*x^18 + 11*x^17 + 6*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 118*x^8 + 86*x^7 + 24*x^6 + 46*x^5 + 36*x^4 + 101*x^3 + 24*x^2 + 77*x + 122, x^27 + 33*x^25 + 18*x^24 + 6*x^23 + 40*x^22 + 94*x^21 + 100*x^20 + 99*x^19 + 8*x^18 + 75*x^17 + 14*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 78*x^8 + 118*x^7 + 8*x^6 + 46*x^5 + 100*x^4 + 5*x^3 + 40*x^2 + 13*x + 82, x^27 + 33*x^25 + 38*x^24 + 54*x^23 + 24*x^22 + 46*x^21 + 12*x^20 + 115*x^19 + 56*x^18 + 59*x^17 + 122*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 122*x^8 + 102*x^7 + 56*x^6 + 62*x^5 + 12*x^4 + 85*x^3 + 24*x^2 + 61*x + 38, x^27 + 33*x^25 + 106*x^24 + 54*x^23 + 8*x^22 + 110*x^21 + 52*x^20 + 115*x^19 + 40*x^18 + 123*x^17 + 86*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 54*x^8 + 102*x^7 + 104*x^6 + 126*x^5 + 52*x^4 + 85*x^3 + 72*x^2 + 125*x + 74, x^27 + 33*x^25 + 6*x^24 + 118*x^23 + 56*x^22 + 46*x^21 + 44*x^20 + 51*x^19 + 24*x^18 + 59*x^17 + 58*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 90*x^8 + 38*x^7 + 88*x^6 + 62*x^5 + 44*x^4 + 21*x^3 + 120*x^2 + 61*x + 38, x^27 + 33*x^25 + 110*x^24 + 102*x^23 + 88*x^22 + 62*x^21 + 28*x^20 + 3*x^19 + 120*x^18 + 107*x^17 + 114*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 50*x^8 + 86*x^7 + 120*x^6 + 14*x^5 + 28*x^4 + 37*x^3 + 88*x^2 + 45*x + 46, x^27 + 33*x^25 + 30*x^24 + 38*x^23 + 56*x^22 + 62*x^21 + 92*x^20 + 67*x^19 + 24*x^18 + 107*x^17 + 98*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 66*x^8 + 22*x^7 + 88*x^6 + 14*x^5 + 92*x^4 + 101*x^3 + 120*x^2 + 45*x + 126, x^27 + 33*x^25 + 110*x^24 + 86*x^23 + 40*x^22 + 110*x^21 + 108*x^20 + 19*x^19 + 40*x^18 + 59*x^17 + 34*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 18*x^8 + 6*x^7 + 8*x^6 + 126*x^5 + 44*x^4 + 117*x^3 + 72*x^2 + 61*x + 30, x^27 + 33*x^25 + 6*x^24 + 38*x^23 + 104*x^22 + 30*x^21 + 92*x^20 + 3*x^19 + 104*x^18 + 75*x^17 + 10*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 122*x^8 + 22*x^7 + 72*x^6 + 110*x^5 + 28*x^4 + 37*x^3 + 8*x^2 + 13*x + 54, x^27 + 33*x^25 + 122*x^24 + 54*x^23 + 104*x^22 + 110*x^21 + 116*x^20 + 115*x^19 + 72*x^18 + 123*x^17 + 38*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 102*x^8 + 102*x^7 + 72*x^6 + 126*x^5 + 116*x^4 + 85*x^3 + 104*x^2 + 125*x + 58, x^27 + 33*x^25 + 86*x^24 + 102*x^23 + 40*x^22 + 94*x^21 + 124*x^20 + 67*x^19 + 40*x^18 + 11*x^17 + 58*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 42*x^8 + 86*x^7 + 8*x^6 + 46*x^5 + 60*x^4 + 101*x^3 + 72*x^2 + 77*x + 6, x^27 + 33*x^25 + 86*x^24 + 38*x^23 + 8*x^22 + 94*x^21 + 28*x^20 + 3*x^19 + 72*x^18 + 11*x^17 + 26*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 106*x^8 + 22*x^7 + 104*x^6 + 46*x^5 + 92*x^4 + 37*x^3 + 104*x^2 + 77*x + 102, x^27 + 33*x^25 + 78*x^24 + 70*x^23 + 88*x^22 + 30*x^21 + 92*x^20 + 35*x^19 + 120*x^18 + 11*x^17 + 18*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 82*x^8 + 54*x^7 + 120*x^6 + 110*x^5 + 92*x^4 + 69*x^3 + 88*x^2 + 77*x + 14, x^27 + 33*x^25 + 6*x^24 + 6*x^23 + 8*x^22 + 126*x^21 + 124*x^20 + 35*x^19 + 72*x^18 + 107*x^17 + 106*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 58*x^8 + 118*x^7 + 104*x^6 + 78*x^5 + 60*x^4 + 69*x^3 + 104*x^2 + 45*x + 22, x^27 + 33*x^25 + 22*x^24 + 102*x^23 + 40*x^22 + 30*x^21 + 60*x^20 + 67*x^19 + 40*x^18 + 75*x^17 + 58*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 106*x^8 + 86*x^7 + 8*x^6 + 110*x^5 + 124*x^4 + 101*x^3 + 72*x^2 + 13*x + 6, x^27 + 33*x^25 + 2*x^24 + 6*x^23 + 40*x^22 + 94*x^21 + 4*x^20 + 99*x^19 + 8*x^18 + 75*x^17 + 94*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 94*x^8 + 118*x^7 + 8*x^6 + 46*x^5 + 4*x^4 + 5*x^3 + 40*x^2 + 13*x + 2, x^27 + 33*x^25 + 82*x^24 + 86*x^23 + 120*x^22 + 110*x^21 + 52*x^20 + 19*x^19 + 56*x^18 + 59*x^17 + 126*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 110*x^8 + 6*x^7 + 24*x^6 + 126*x^5 + 116*x^4 + 117*x^3 + 24*x^2 + 61*x + 2, x^27 + 33*x^25 + 6*x^24 + 22*x^23 + 24*x^22 + 14*x^21 + 76*x^20 + 19*x^19 + 56*x^18 + 91*x^17 + 26*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 26*x^8 + 70*x^7 + 56*x^6 + 30*x^5 + 76*x^4 + 117*x^3 + 24*x^2 + 93*x + 6, x^27 + 33*x^25 + 26*x^24 + 54*x^23 + 40*x^22 + 110*x^21 + 116*x^20 + 115*x^19 + 8*x^18 + 123*x^17 + 70*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 70*x^8 + 102*x^7 + 8*x^6 + 126*x^5 + 116*x^4 + 85*x^3 + 40*x^2 + 125*x + 26, x^27 + 33*x^25 + 54*x^24 + 102*x^23 + 72*x^22 + 30*x^21 + 28*x^20 + 67*x^19 + 8*x^18 + 75*x^17 + 122*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 10*x^8 + 86*x^7 + 40*x^6 + 110*x^5 + 92*x^4 + 101*x^3 + 40*x^2 + 13*x + 6, x^27 + 33*x^25 + 42*x^24 + 38*x^23 + 88*x^22 + 94*x^21 + 68*x^20 + 3*x^19 + 88*x^18 + 11*x^17 + 6*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 86*x^8 + 22*x^7 + 120*x^6 + 46*x^5 + 4*x^4 + 37*x^3 + 56*x^2 + 77*x + 58, x^27 + 33*x^25 + 110*x^24 + 70*x^23 + 88*x^22 + 94*x^21 + 92*x^20 + 35*x^19 + 120*x^18 + 75*x^17 + 50*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 50*x^8 + 54*x^7 + 120*x^6 + 46*x^5 + 92*x^4 + 69*x^3 + 88*x^2 + 13*x + 110, x^27 + 33*x^25 + 18*x^24 + 22*x^23 + 120*x^22 + 110*x^21 + 116*x^20 + 83*x^19 + 56*x^18 + 59*x^17 + 126*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 46*x^8 + 70*x^7 + 24*x^6 + 126*x^5 + 52*x^4 + 53*x^3 + 24*x^2 + 61*x + 2, x^27 + 33*x^25 + 50*x^24 + 6*x^23 + 8*x^22 + 30*x^21 + 68*x^20 + 99*x^19 + 40*x^18 + 11*x^17 + 78*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 110*x^8 + 118*x^7 + 104*x^6 + 110*x^5 + 68*x^4 + 5*x^3 + 72*x^2 + 77*x + 82, x^27 + 33*x^25 + 86*x^24 + 54*x^23 + 24*x^22 + 46*x^21 + 44*x^20 + 115*x^19 + 56*x^18 + 59*x^17 + 10*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 74*x^8 + 102*x^7 + 56*x^6 + 62*x^5 + 44*x^4 + 85*x^3 + 24*x^2 + 61*x + 22, x^27 + 33*x^25 + 74*x^24 + 6*x^23 + 24*x^22 + 126*x^21 + 4*x^20 + 35*x^19 + 24*x^18 + 107*x^17 + 102*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 54*x^8 + 118*x^7 + 56*x^6 + 78*x^5 + 68*x^4 + 69*x^3 + 120*x^2 + 45*x + 90, x^27 + 33*x^25 + 74*x^24 + 22*x^23 + 104*x^22 + 14*x^21 + 20*x^20 + 19*x^19 + 72*x^18 + 91*x^17 + 86*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 22*x^8 + 70*x^7 + 72*x^6 + 30*x^5 + 20*x^4 + 117*x^3 + 104*x^2 + 93*x + 10, x^27 + 33*x^25 + 6*x^24 + 70*x^23 + 104*x^22 + 126*x^21 + 28*x^20 + 99*x^19 + 104*x^18 + 107*x^17 + 74*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 122*x^8 + 54*x^7 + 72*x^6 + 78*x^5 + 92*x^4 + 5*x^3 + 8*x^2 + 45*x + 118, x^27 + 33*x^25 + 6*x^24 + 6*x^23 + 40*x^22 + 62*x^21 + 92*x^20 + 35*x^19 + 40*x^18 + 43*x^17 + 10*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 122*x^8 + 118*x^7 + 8*x^6 + 14*x^5 + 28*x^4 + 69*x^3 + 72*x^2 + 109*x + 54, x^27 + 33*x^25 + 106*x^24 + 70*x^23 + 56*x^22 + 62*x^21 + 100*x^20 + 99*x^19 + 120*x^18 + 43*x^17 + 38*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 86*x^8 + 54*x^7 + 88*x^6 + 14*x^5 + 36*x^4 + 5*x^3 + 88*x^2 + 109*x + 90, x^27 + 33*x^25 + 6*x^24 + 118*x^23 + 88*x^22 + 46*x^21 + 76*x^20 + 51*x^19 + 120*x^18 + 59*x^17 + 26*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 26*x^8 + 38*x^7 + 120*x^6 + 62*x^5 + 76*x^4 + 21*x^3 + 88*x^2 + 61*x + 6, x^27 + 33*x^25 + 46*x^24 + 6*x^23 + 56*x^22 + 94*x^21 + 124*x^20 + 99*x^19 + 24*x^18 + 75*x^17 + 82*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 50*x^8 + 118*x^7 + 88*x^6 + 46*x^5 + 124*x^4 + 5*x^3 + 120*x^2 + 13*x + 14, x^27 + 33*x^25 + 110*x^24 + 70*x^23 + 56*x^22 + 94*x^21 + 60*x^20 + 35*x^19 + 24*x^18 + 75*x^17 + 82*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 114*x^8 + 54*x^7 + 88*x^6 + 46*x^5 + 60*x^4 + 69*x^3 + 120*x^2 + 13*x + 14, x^27 + 33*x^25 + 46*x^24 + 54*x^23 + 40*x^22 + 14*x^21 + 44*x^20 + 51*x^19 + 40*x^18 + 27*x^17 + 34*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 82*x^8 + 102*x^7 + 8*x^6 + 30*x^5 + 108*x^4 + 21*x^3 + 72*x^2 + 29*x + 30, x^27 + 33*x^25 + 30*x^24 + 70*x^23 + 24*x^22 + 30*x^21 + 124*x^20 + 35*x^19 + 56*x^18 + 11*x^17 + 66*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 2*x^8 + 54*x^7 + 56*x^6 + 110*x^5 + 124*x^4 + 69*x^3 + 24*x^2 + 77*x + 94, x^27 + 33*x^25 + 118*x^24 + 102*x^23 + 40*x^22 + 94*x^21 + 60*x^20 + 67*x^19 + 40*x^18 + 11*x^17 + 26*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 10*x^8 + 86*x^7 + 8*x^6 + 46*x^5 + 124*x^4 + 101*x^3 + 72*x^2 + 77*x + 38, x^27 + 33*x^25 + 6*x^24 + 22*x^23 + 88*x^22 + 14*x^21 + 12*x^20 + 19*x^19 + 120*x^18 + 91*x^17 + 90*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 26*x^8 + 70*x^7 + 120*x^6 + 30*x^5 + 12*x^4 + 117*x^3 + 88*x^2 + 93*x + 70, x^27 + 33*x^25 + 54*x^24 + 118*x^23 + 120*x^22 + 46*x^21 + 12*x^20 + 51*x^19 + 88*x^18 + 59*x^17 + 10*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 42*x^8 + 38*x^7 + 24*x^6 + 62*x^5 + 12*x^4 + 21*x^3 + 56*x^2 + 61*x + 86, x^27 + 33*x^25 + 86*x^24 + 6*x^23 + 72*x^22 + 126*x^21 + 28*x^20 + 35*x^19 + 8*x^18 + 107*x^17 + 26*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 106*x^8 + 118*x^7 + 40*x^6 + 78*x^5 + 92*x^4 + 69*x^3 + 40*x^2 + 45*x + 102, x^27 + 33*x^25 + 10*x^24 + 70*x^23 + 120*x^22 + 62*x^21 + 100*x^20 + 99*x^19 + 56*x^18 + 43*x^17 + 70*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 54*x^8 + 54*x^7 + 24*x^6 + 14*x^5 + 36*x^4 + 5*x^3 + 24*x^2 + 109*x + 58, x^27 + 33*x^25 + 6*x^24 + 38*x^23 + 40*x^22 + 30*x^21 + 28*x^20 + 3*x^19 + 40*x^18 + 75*x^17 + 74*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 122*x^8 + 22*x^7 + 8*x^6 + 110*x^5 + 92*x^4 + 37*x^3 + 72*x^2 + 13*x + 118, x^27 + 33*x^25 + 66*x^24 + 70*x^23 + 40*x^22 + 94*x^21 + 68*x^20 + 35*x^19 + 8*x^18 + 75*x^17 + 94*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 30*x^8 + 54*x^7 + 8*x^6 + 46*x^5 + 68*x^4 + 69*x^3 + 40*x^2 + 13*x + 2, x^27 + 33*x^25 + 78*x^24 + 70*x^23 + 24*x^22 + 30*x^21 + 28*x^20 + 35*x^19 + 56*x^18 + 11*x^17 + 82*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 82*x^8 + 54*x^7 + 56*x^6 + 110*x^5 + 28*x^4 + 69*x^3 + 24*x^2 + 77*x + 78, x^27 + 33*x^25 + 50*x^24 + 54*x^23 + 88*x^22 + 14*x^21 + 20*x^20 + 51*x^19 + 88*x^18 + 27*x^17 + 126*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 78*x^8 + 102*x^7 + 120*x^6 + 30*x^5 + 84*x^4 + 21*x^3 + 56*x^2 + 29*x + 66, x^27 + 33*x^25 + 38*x^24 + 86*x^23 + 120*x^22 + 78*x^21 + 108*x^20 + 83*x^19 + 88*x^18 + 27*x^17 + 26*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 58*x^8 + 6*x^7 + 24*x^6 + 94*x^5 + 108*x^4 + 53*x^3 + 56*x^2 + 29*x + 70, x^27 + 33*x^25 + 70*x^24 + 118*x^23 + 24*x^22 + 110*x^21 + 76*x^20 + 51*x^19 + 56*x^18 + 123*x^17 + 90*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 90*x^8 + 38*x^7 + 56*x^6 + 126*x^5 + 76*x^4 + 21*x^3 + 24*x^2 + 125*x + 70, x^27 + 33*x^25 + 46*x^24 + 22*x^23 + 8*x^22 + 110*x^21 + 12*x^20 + 83*x^19 + 72*x^18 + 59*x^17 + 66*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 18*x^8 + 70*x^7 + 104*x^6 + 126*x^5 + 76*x^4 + 53*x^3 + 104*x^2 + 61*x + 62, x^27 + 33*x^25 + 58*x^24 + 102*x^23 + 56*x^22 + 94*x^21 + 68*x^20 + 67*x^19 + 120*x^18 + 11*x^17 + 22*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 6*x^8 + 86*x^7 + 88*x^6 + 46*x^5 + 4*x^4 + 101*x^3 + 88*x^2 + 77*x + 106, x^27 + 33*x^25 + 122*x^24 + 86*x^23 + 8*x^22 + 14*x^21 + 20*x^20 + 83*x^19 + 40*x^18 + 91*x^17 + 6*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 38*x^8 + 6*x^7 + 104*x^6 + 30*x^5 + 20*x^4 + 53*x^3 + 72*x^2 + 93*x + 26, x^27 + 33*x^25 + 38*x^24 + 22*x^23 + 120*x^22 + 78*x^21 + 44*x^20 + 19*x^19 + 88*x^18 + 27*x^17 + 90*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 58*x^8 + 70*x^7 + 24*x^6 + 94*x^5 + 44*x^4 + 117*x^3 + 56*x^2 + 29*x + 6, x^27 + 33*x^25 + 54*x^24 + 86*x^23 + 88*x^22 + 78*x^21 + 44*x^20 + 83*x^19 + 120*x^18 + 27*x^17 + 106*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 106*x^8 + 6*x^7 + 120*x^6 + 94*x^5 + 44*x^4 + 53*x^3 + 88*x^2 + 29*x + 54, x^27 + 33*x^25 + 94*x^24 + 38*x^23 + 56*x^22 + 62*x^21 + 92*x^20 + 67*x^19 + 24*x^18 + 107*x^17 + 34*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 2*x^8 + 22*x^7 + 88*x^6 + 14*x^5 + 92*x^4 + 101*x^3 + 120*x^2 + 45*x + 62, x^27 + 33*x^25 + 86*x^24 + 118*x^23 + 56*x^22 + 110*x^21 + 76*x^20 + 51*x^19 + 24*x^18 + 123*x^17 + 106*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 10*x^8 + 38*x^7 + 88*x^6 + 126*x^5 + 76*x^4 + 21*x^3 + 120*x^2 + 125*x + 118, x^27 + 33*x^25 + 94*x^24 + 86*x^23 + 104*x^22 + 110*x^21 + 76*x^20 + 19*x^19 + 104*x^18 + 59*x^17 + 50*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 34*x^8 + 6*x^7 + 72*x^6 + 126*x^5 + 12*x^4 + 117*x^3 + 8*x^2 + 61*x + 14, x^27 + 33*x^25 + 42*x^24 + 70*x^23 + 120*x^22 + 126*x^21 + 100*x^20 + 99*x^19 + 56*x^18 + 107*x^17 + 102*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 22*x^8 + 54*x^7 + 24*x^6 + 78*x^5 + 36*x^4 + 5*x^3 + 24*x^2 + 45*x + 26, x^27 + 33*x^25 + 78*x^24 + 118*x^23 + 104*x^22 + 14*x^21 + 108*x^20 + 115*x^19 + 104*x^18 + 27*x^17 + 2*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 50*x^8 + 38*x^7 + 72*x^6 + 30*x^5 + 44*x^4 + 85*x^3 + 8*x^2 + 29*x + 62, x^27 + 33*x^25 + 66*x^24 + 22*x^23 + 24*x^22 + 46*x^21 + 116*x^20 + 83*x^19 + 24*x^18 + 123*x^17 + 46*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 62*x^8 + 70*x^7 + 56*x^6 + 62*x^5 + 52*x^4 + 53*x^3 + 120*x^2 + 125*x + 18, x^27 + 33*x^25 + 106*x^24 + 38*x^23 + 24*x^22 + 30*x^21 + 68*x^20 + 3*x^19 + 24*x^18 + 75*x^17 + 70*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 22*x^8 + 22*x^7 + 56*x^6 + 110*x^5 + 4*x^4 + 37*x^3 + 120*x^2 + 13*x + 122, x^27 + 33*x^25 + 2*x^24 + 102*x^23 + 72*x^22 + 126*x^21 + 100*x^20 + 3*x^19 + 104*x^18 + 43*x^17 + 126*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 30*x^8 + 86*x^7 + 40*x^6 + 78*x^5 + 100*x^4 + 37*x^3 + 8*x^2 + 109*x + 34, x^27 + 33*x^25 + 118*x^24 + 118*x^23 + 88*x^22 + 46*x^21 + 108*x^20 + 51*x^19 + 120*x^18 + 59*x^17 + 106*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 42*x^8 + 38*x^7 + 120*x^6 + 62*x^5 + 108*x^4 + 21*x^3 + 88*x^2 + 61*x + 54, x^27 + 33*x^25 + 46*x^24 + 86*x^23 + 40*x^22 + 46*x^21 + 44*x^20 + 19*x^19 + 40*x^18 + 123*x^17 + 34*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 82*x^8 + 6*x^7 + 8*x^6 + 62*x^5 + 108*x^4 + 117*x^3 + 72*x^2 + 125*x + 30, x^27 + 33*x^25 + 14*x^24 + 86*x^23 + 72*x^22 + 46*x^21 + 12*x^20 + 19*x^19 + 8*x^18 + 123*x^17 + 34*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 50*x^8 + 6*x^7 + 40*x^6 + 62*x^5 + 76*x^4 + 117*x^3 + 40*x^2 + 125*x + 94, x^27 + 33*x^25 + 86*x^24 + 86*x^23 + 56*x^22 + 78*x^21 + 76*x^20 + 83*x^19 + 24*x^18 + 27*x^17 + 106*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 10*x^8 + 6*x^7 + 88*x^6 + 94*x^5 + 76*x^4 + 53*x^3 + 120*x^2 + 29*x + 118, x^27 + 33*x^25 + 34*x^24 + 118*x^23 + 24*x^22 + 78*x^21 + 116*x^20 + 115*x^19 + 24*x^18 + 91*x^17 + 14*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 94*x^8 + 38*x^7 + 56*x^6 + 94*x^5 + 52*x^4 + 85*x^3 + 120*x^2 + 93*x + 50, x^27 + 33*x^25 + 30*x^24 + 54*x^23 + 40*x^22 + 78*x^21 + 12*x^20 + 51*x^19 + 40*x^18 + 91*x^17 + 50*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 98*x^8 + 102*x^7 + 8*x^6 + 94*x^5 + 76*x^4 + 21*x^3 + 72*x^2 + 93*x + 14, x^27 + 33*x^25 + 66*x^24 + 102*x^23 + 40*x^22 + 126*x^21 + 68*x^20 + 3*x^19 + 8*x^18 + 43*x^17 + 94*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 30*x^8 + 86*x^7 + 8*x^6 + 78*x^5 + 68*x^4 + 37*x^3 + 40*x^2 + 109*x + 2, x^27 + 33*x^25 + 42*x^24 + 86*x^23 + 104*x^22 + 78*x^21 + 84*x^20 + 83*x^19 + 72*x^18 + 27*x^17 + 118*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 54*x^8 + 6*x^7 + 72*x^6 + 94*x^5 + 84*x^4 + 53*x^3 + 104*x^2 + 29*x + 106, x^27 + 33*x^25 + 98*x^24 + 54*x^23 + 56*x^22 + 14*x^21 + 20*x^20 + 51*x^19 + 120*x^18 + 27*x^17 + 46*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 94*x^8 + 102*x^7 + 88*x^6 + 30*x^5 + 84*x^4 + 21*x^3 + 88*x^2 + 29*x + 82, x^27 + 33*x^25 + 122*x^24 + 86*x^23 + 72*x^22 + 14*x^21 + 84*x^20 + 83*x^19 + 104*x^18 + 91*x^17 + 70*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 38*x^8 + 6*x^7 + 40*x^6 + 30*x^5 + 84*x^4 + 53*x^3 + 8*x^2 + 93*x + 90, x^27 + 33*x^25 + 2*x^24 + 38*x^23 + 8*x^22 + 62*x^21 + 36*x^20 + 67*x^19 + 40*x^18 + 107*x^17 + 62*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 30*x^8 + 22*x^7 + 104*x^6 + 14*x^5 + 36*x^4 + 101*x^3 + 72*x^2 + 45*x + 98, x^27 + 33*x^25 + 14*x^24 + 22*x^23 + 72*x^22 + 46*x^21 + 76*x^20 + 83*x^19 + 8*x^18 + 123*x^17 + 98*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 50*x^8 + 70*x^7 + 40*x^6 + 62*x^5 + 12*x^4 + 53*x^3 + 40*x^2 + 125*x + 30, x^27 + 33*x^25 + 78*x^24 + 22*x^23 + 40*x^22 + 110*x^21 + 108*x^20 + 83*x^19 + 40*x^18 + 59*x^17 + 2*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 50*x^8 + 70*x^7 + 8*x^6 + 126*x^5 + 44*x^4 + 53*x^3 + 72*x^2 + 61*x + 62, x^27 + 33*x^25 + 78*x^24 + 22*x^23 + 8*x^22 + 46*x^21 + 12*x^20 + 83*x^19 + 72*x^18 + 123*x^17 + 98*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 114*x^8 + 70*x^7 + 104*x^6 + 62*x^5 + 76*x^4 + 53*x^3 + 104*x^2 + 125*x + 30, x^27 + 33*x^25 + 74*x^24 + 86*x^23 + 8*x^22 + 78*x^21 + 52*x^20 + 83*x^19 + 40*x^18 + 27*x^17 + 54*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 86*x^8 + 6*x^7 + 104*x^6 + 94*x^5 + 52*x^4 + 53*x^3 + 72*x^2 + 29*x + 106, x^27 + 33*x^25 + 46*x^24 + 38*x^23 + 88*x^22 + 62*x^21 + 92*x^20 + 67*x^19 + 120*x^18 + 107*x^17 + 114*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 114*x^8 + 22*x^7 + 120*x^6 + 14*x^5 + 92*x^4 + 101*x^3 + 88*x^2 + 45*x + 46, x^27 + 33*x^25 + 38*x^24 + 6*x^23 + 104*x^22 + 62*x^21 + 92*x^20 + 35*x^19 + 104*x^18 + 43*x^17 + 42*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 90*x^8 + 118*x^7 + 72*x^6 + 14*x^5 + 28*x^4 + 69*x^3 + 8*x^2 + 109*x + 22, x^27 + 33*x^25 + 126*x^24 + 54*x^23 + 40*x^22 + 14*x^21 + 12*x^20 + 51*x^19 + 40*x^18 + 27*x^17 + 18*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 2*x^8 + 102*x^7 + 8*x^6 + 30*x^5 + 76*x^4 + 21*x^3 + 72*x^2 + 29*x + 46, x^27 + 33*x^25 + 94*x^24 + 118*x^23 + 104*x^22 + 78*x^21 + 12*x^20 + 115*x^19 + 104*x^18 + 91*x^17 + 114*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 34*x^8 + 38*x^7 + 72*x^6 + 94*x^5 + 76*x^4 + 85*x^3 + 8*x^2 + 93*x + 78, x^27 + 33*x^25 + 38*x^24 + 102*x^23 + 8*x^22 + 30*x^21 + 124*x^20 + 67*x^19 + 72*x^18 + 75*x^17 + 10*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 26*x^8 + 86*x^7 + 104*x^6 + 110*x^5 + 60*x^4 + 101*x^3 + 104*x^2 + 13*x + 118, x^27 + 33*x^25 + 90*x^24 + 86*x^23 + 8*x^22 + 14*x^21 + 84*x^20 + 83*x^19 + 40*x^18 + 91*x^17 + 38*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 70*x^8 + 6*x^7 + 104*x^6 + 30*x^5 + 84*x^4 + 53*x^3 + 72*x^2 + 93*x + 122, x^27 + 33*x^25 + 54*x^24 + 22*x^23 + 24*x^22 + 14*x^21 + 108*x^20 + 19*x^19 + 56*x^18 + 91*x^17 + 42*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 106*x^8 + 70*x^7 + 56*x^6 + 30*x^5 + 108*x^4 + 117*x^3 + 24*x^2 + 93*x + 118, x^27 + 33*x^25 + 62*x^24 + 54*x^23 + 40*x^22 + 78*x^21 + 76*x^20 + 51*x^19 + 40*x^18 + 91*x^17 + 18*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 66*x^8 + 102*x^7 + 8*x^6 + 94*x^5 + 12*x^4 + 21*x^3 + 72*x^2 + 93*x + 46, x^27 + 33*x^25 + 38*x^24 + 54*x^23 + 120*x^22 + 46*x^21 + 108*x^20 + 115*x^19 + 88*x^18 + 59*x^17 + 26*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 58*x^8 + 102*x^7 + 24*x^6 + 62*x^5 + 108*x^4 + 85*x^3 + 56*x^2 + 61*x + 70, x^27 + 33*x^25 + 66*x^24 + 70*x^23 + 72*x^22 + 30*x^21 + 36*x^20 + 35*x^19 + 104*x^18 + 11*x^17 + 126*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 94*x^8 + 54*x^7 + 40*x^6 + 110*x^5 + 36*x^4 + 69*x^3 + 8*x^2 + 77*x + 34, x^27 + 33*x^25 + 42*x^24 + 38*x^23 + 24*x^22 + 94*x^21 + 4*x^20 + 3*x^19 + 24*x^18 + 11*x^17 + 70*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 86*x^8 + 22*x^7 + 56*x^6 + 46*x^5 + 68*x^4 + 37*x^3 + 120*x^2 + 77*x + 122, x^27 + 33*x^25 + 114*x^24 + 118*x^23 + 56*x^22 + 78*x^21 + 116*x^20 + 115*x^19 + 120*x^18 + 91*x^17 + 94*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 78*x^8 + 38*x^7 + 88*x^6 + 94*x^5 + 52*x^4 + 85*x^3 + 88*x^2 + 93*x + 34, x^27 + 33*x^25 + 62*x^24 + 54*x^23 + 104*x^22 + 14*x^21 + 76*x^20 + 51*x^19 + 104*x^18 + 27*x^17 + 18*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 66*x^8 + 102*x^7 + 72*x^6 + 30*x^5 + 12*x^4 + 21*x^3 + 8*x^2 + 29*x + 46, x^27 + 33*x^25 + 50*x^24 + 118*x^23 + 56*x^22 + 14*x^21 + 52*x^20 + 115*x^19 + 120*x^18 + 27*x^17 + 94*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 14*x^8 + 38*x^7 + 88*x^6 + 30*x^5 + 116*x^4 + 85*x^3 + 88*x^2 + 29*x + 34, x^27 + 33*x^25 + 102*x^24 + 22*x^23 + 56*x^22 + 78*x^21 + 108*x^20 + 19*x^19 + 24*x^18 + 27*x^17 + 90*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 122*x^8 + 70*x^7 + 88*x^6 + 94*x^5 + 108*x^4 + 117*x^3 + 120*x^2 + 29*x + 6, x^27 + 33*x^25 + 106*x^24 + 70*x^23 + 120*x^22 + 126*x^21 + 100*x^20 + 99*x^19 + 56*x^18 + 107*x^17 + 38*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 86*x^8 + 54*x^7 + 24*x^6 + 78*x^5 + 36*x^4 + 5*x^3 + 24*x^2 + 45*x + 90, x^27 + 33*x^25 + 78*x^24 + 86*x^23 + 40*x^22 + 46*x^21 + 108*x^20 + 19*x^19 + 40*x^18 + 123*x^17 + 2*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 50*x^8 + 6*x^7 + 8*x^6 + 62*x^5 + 44*x^4 + 117*x^3 + 72*x^2 + 125*x + 62, x^27 + 33*x^25 + 46*x^24 + 86*x^23 + 8*x^22 + 110*x^21 + 76*x^20 + 19*x^19 + 72*x^18 + 59*x^17 + 2*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 18*x^8 + 6*x^7 + 104*x^6 + 126*x^5 + 12*x^4 + 117*x^3 + 104*x^2 + 61*x + 126, x^27 + 33*x^25 + 54*x^24 + 102*x^23 + 104*x^22 + 30*x^21 + 60*x^20 + 67*x^19 + 104*x^18 + 75*x^17 + 90*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 74*x^8 + 86*x^7 + 72*x^6 + 110*x^5 + 124*x^4 + 101*x^3 + 8*x^2 + 13*x + 102, x^27 + 33*x^25 + 34*x^24 + 118*x^23 + 88*x^22 + 78*x^21 + 52*x^20 + 115*x^19 + 88*x^18 + 91*x^17 + 78*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 94*x^8 + 38*x^7 + 120*x^6 + 94*x^5 + 116*x^4 + 85*x^3 + 56*x^2 + 93*x + 114, x^27 + 33*x^25 + 26*x^24 + 70*x^23 + 88*x^22 + 126*x^21 + 100*x^20 + 99*x^19 + 88*x^18 + 107*x^17 + 86*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 102*x^8 + 54*x^7 + 120*x^6 + 78*x^5 + 36*x^4 + 5*x^3 + 56*x^2 + 45*x + 106, x^27 + 33*x^25 + 70*x^24 + 86*x^23 + 120*x^22 + 78*x^21 + 44*x^20 + 83*x^19 + 88*x^18 + 27*x^17 + 122*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 26*x^8 + 6*x^7 + 24*x^6 + 94*x^5 + 44*x^4 + 53*x^3 + 56*x^2 + 29*x + 102, x^27 + 33*x^25 + 6*x^24 + 22*x^23 + 120*x^22 + 14*x^21 + 44*x^20 + 19*x^19 + 88*x^18 + 91*x^17 + 58*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 90*x^8 + 70*x^7 + 24*x^6 + 30*x^5 + 44*x^4 + 117*x^3 + 56*x^2 + 93*x + 38, x^27 + 33*x^25 + 22*x^24 + 54*x^23 + 56*x^22 + 46*x^21 + 76*x^20 + 115*x^19 + 24*x^18 + 59*x^17 + 42*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 74*x^8 + 102*x^7 + 88*x^6 + 62*x^5 + 76*x^4 + 85*x^3 + 120*x^2 + 61*x + 54, x^27 + 33*x^25 + 6*x^24 + 86*x^23 + 24*x^22 + 14*x^21 + 12*x^20 + 83*x^19 + 56*x^18 + 91*x^17 + 90*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 26*x^8 + 6*x^7 + 56*x^6 + 30*x^5 + 12*x^4 + 53*x^3 + 24*x^2 + 93*x + 70, x^27 + 33*x^25 + 46*x^24 + 70*x^23 + 24*x^22 + 94*x^21 + 28*x^20 + 35*x^19 + 56*x^18 + 75*x^17 + 50*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 114*x^8 + 54*x^7 + 56*x^6 + 46*x^5 + 28*x^4 + 69*x^3 + 24*x^2 + 13*x + 110, x^27 + 33*x^25 + 30*x^24 + 22*x^23 + 40*x^22 + 46*x^21 + 12*x^20 + 83*x^19 + 40*x^18 + 123*x^17 + 50*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 98*x^8 + 70*x^7 + 8*x^6 + 62*x^5 + 76*x^4 + 53*x^3 + 72*x^2 + 125*x + 14, x^27 + 33*x^25 + 110*x^24 + 22*x^23 + 8*x^22 + 110*x^21 + 12*x^20 + 83*x^19 + 72*x^18 + 59*x^17 + 2*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 82*x^8 + 70*x^7 + 104*x^6 + 126*x^5 + 76*x^4 + 53*x^3 + 104*x^2 + 61*x + 126, x^27 + 33*x^25 + 118*x^24 + 86*x^23 + 24*x^22 + 14*x^21 + 44*x^20 + 83*x^19 + 56*x^18 + 91*x^17 + 42*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 42*x^8 + 6*x^7 + 56*x^6 + 30*x^5 + 44*x^4 + 53*x^3 + 24*x^2 + 93*x + 118, x^27 + 33*x^25 + 62*x^24 + 22*x^23 + 72*x^22 + 46*x^21 + 108*x^20 + 83*x^19 + 8*x^18 + 123*x^17 + 114*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 2*x^8 + 70*x^7 + 40*x^6 + 62*x^5 + 44*x^4 + 53*x^3 + 40*x^2 + 125*x + 14, x^27 + 33*x^25 + 38*x^24 + 70*x^23 + 40*x^22 + 62*x^21 + 92*x^20 + 99*x^19 + 40*x^18 + 43*x^17 + 42*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 90*x^8 + 54*x^7 + 8*x^6 + 14*x^5 + 28*x^4 + 5*x^3 + 72*x^2 + 109*x + 22, x^27 + 33*x^25 + 114*x^24 + 22*x^23 + 88*x^22 + 110*x^21 + 20*x^20 + 83*x^19 + 88*x^18 + 59*x^17 + 62*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 14*x^8 + 70*x^7 + 120*x^6 + 126*x^5 + 84*x^4 + 53*x^3 + 56*x^2 + 61*x + 2, x^27 + 33*x^25 + 118*x^24 + 118*x^23 + 24*x^22 + 46*x^21 + 44*x^20 + 51*x^19 + 56*x^18 + 59*x^17 + 42*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 42*x^8 + 38*x^7 + 56*x^6 + 62*x^5 + 44*x^4 + 21*x^3 + 24*x^2 + 61*x + 118, x^27 + 33*x^25 + 106*x^24 + 118*x^23 + 72*x^22 + 46*x^21 + 116*x^20 + 51*x^19 + 104*x^18 + 59*x^17 + 22*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 54*x^8 + 38*x^7 + 40*x^6 + 62*x^5 + 116*x^4 + 21*x^3 + 8*x^2 + 61*x + 10, x^27 + 33*x^25 + 122*x^24 + 38*x^23 + 120*x^22 + 30*x^21 + 4*x^20 + 3*x^19 + 56*x^18 + 75*x^17 + 22*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 70*x^8 + 22*x^7 + 24*x^6 + 110*x^5 + 68*x^4 + 37*x^3 + 24*x^2 + 13*x + 106, x^27 + 33*x^25 + 90*x^24 + 38*x^23 + 120*x^22 + 94*x^21 + 4*x^20 + 3*x^19 + 56*x^18 + 11*x^17 + 118*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 102*x^8 + 22*x^7 + 24*x^6 + 46*x^5 + 68*x^4 + 37*x^3 + 24*x^2 + 77*x + 10, x^27 + 33*x^25 + 102*x^24 + 38*x^23 + 40*x^22 + 30*x^21 + 92*x^20 + 3*x^19 + 40*x^18 + 75*x^17 + 106*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 26*x^8 + 22*x^7 + 8*x^6 + 110*x^5 + 28*x^4 + 37*x^3 + 72*x^2 + 13*x + 86, x^27 + 33*x^25 + 58*x^24 + 86*x^23 + 8*x^22 + 14*x^21 + 20*x^20 + 83*x^19 + 40*x^18 + 91*x^17 + 70*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 102*x^8 + 6*x^7 + 104*x^6 + 30*x^5 + 20*x^4 + 53*x^3 + 72*x^2 + 93*x + 90, x^27 + 33*x^25 + 114*x^24 + 118*x^23 + 88*x^22 + 78*x^21 + 20*x^20 + 115*x^19 + 88*x^18 + 91*x^17 + 62*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 14*x^8 + 38*x^7 + 120*x^6 + 94*x^5 + 84*x^4 + 85*x^3 + 56*x^2 + 93*x + 2, x^27 + 33*x^25 + 10*x^24 + 54*x^23 + 8*x^22 + 46*x^21 + 52*x^20 + 115*x^19 + 40*x^18 + 59*x^17 + 118*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 22*x^8 + 102*x^7 + 104*x^6 + 62*x^5 + 52*x^4 + 85*x^3 + 72*x^2 + 61*x + 42, x^27 + 33*x^25 + 22*x^24 + 70*x^23 + 72*x^22 + 126*x^21 + 92*x^20 + 99*x^19 + 8*x^18 + 107*x^17 + 26*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 42*x^8 + 54*x^7 + 40*x^6 + 78*x^5 + 28*x^4 + 5*x^3 + 40*x^2 + 45*x + 102, x^27 + 33*x^25 + 2*x^24 + 102*x^23 + 104*x^22 + 126*x^21 + 4*x^20 + 3*x^19 + 72*x^18 + 43*x^17 + 94*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 94*x^8 + 86*x^7 + 72*x^6 + 78*x^5 + 4*x^4 + 37*x^3 + 104*x^2 + 109*x + 2, x^27 + 33*x^25 + 94*x^24 + 70*x^23 + 56*x^22 + 94*x^21 + 92*x^20 + 35*x^19 + 24*x^18 + 75*x^17 + 34*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 2*x^8 + 54*x^7 + 88*x^6 + 46*x^5 + 92*x^4 + 69*x^3 + 120*x^2 + 13*x + 62, x^27 + 33*x^25 + 110*x^24 + 22*x^23 + 40*x^22 + 46*x^21 + 108*x^20 + 83*x^19 + 40*x^18 + 123*x^17 + 34*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 18*x^8 + 70*x^7 + 8*x^6 + 62*x^5 + 44*x^4 + 53*x^3 + 72*x^2 + 125*x + 30, x^27 + 33*x^25 + 2*x^24 + 54*x^23 + 24*x^22 + 78*x^21 + 116*x^20 + 51*x^19 + 24*x^18 + 91*x^17 + 110*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 126*x^8 + 102*x^7 + 56*x^6 + 94*x^5 + 52*x^4 + 21*x^3 + 120*x^2 + 93*x + 82, x^27 + 33*x^25 + 50*x^24 + 6*x^23 + 40*x^22 + 30*x^21 + 100*x^20 + 99*x^19 + 8*x^18 + 11*x^17 + 46*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 46*x^8 + 118*x^7 + 8*x^6 + 110*x^5 + 100*x^4 + 5*x^3 + 40*x^2 + 77*x + 50, x^27 + 33*x^25 + 94*x^24 + 86*x^23 + 104*x^22 + 46*x^21 + 12*x^20 + 19*x^19 + 104*x^18 + 123*x^17 + 114*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 34*x^8 + 6*x^7 + 72*x^6 + 62*x^5 + 76*x^4 + 117*x^3 + 8*x^2 + 125*x + 78, x^27 + 33*x^25 + 82*x^24 + 54*x^23 + 88*x^22 + 14*x^21 + 84*x^20 + 51*x^19 + 88*x^18 + 27*x^17 + 94*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 46*x^8 + 102*x^7 + 120*x^6 + 30*x^5 + 20*x^4 + 21*x^3 + 56*x^2 + 29*x + 98, x^27 + 33*x^25 + 78*x^24 + 70*x^23 + 24*x^22 + 94*x^21 + 92*x^20 + 35*x^19 + 56*x^18 + 75*x^17 + 18*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 82*x^8 + 54*x^7 + 56*x^6 + 46*x^5 + 92*x^4 + 69*x^3 + 24*x^2 + 13*x + 14, x^27 + 33*x^25 + 114*x^24 + 54*x^23 + 120*x^22 + 78*x^21 + 116*x^20 + 51*x^19 + 56*x^18 + 91*x^17 + 94*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 78*x^8 + 102*x^7 + 24*x^6 + 94*x^5 + 52*x^4 + 21*x^3 + 24*x^2 + 93*x + 34, x^27 + 33*x^25 + 70*x^24 + 102*x^23 + 72*x^22 + 94*x^21 + 60*x^20 + 67*x^19 + 8*x^18 + 11*x^17 + 106*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 122*x^8 + 86*x^7 + 40*x^6 + 46*x^5 + 124*x^4 + 101*x^3 + 40*x^2 + 77*x + 22, x^27 + 33*x^25 + 6*x^24 + 86*x^23 + 24*x^22 + 78*x^21 + 76*x^20 + 83*x^19 + 56*x^18 + 27*x^17 + 26*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 26*x^8 + 6*x^7 + 56*x^6 + 94*x^5 + 76*x^4 + 53*x^3 + 24*x^2 + 29*x + 6, x^27 + 33*x^25 + 22*x^24 + 54*x^23 + 24*x^22 + 46*x^21 + 44*x^20 + 115*x^19 + 56*x^18 + 59*x^17 + 74*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 10*x^8 + 102*x^7 + 56*x^6 + 62*x^5 + 44*x^4 + 85*x^3 + 24*x^2 + 61*x + 86, x^27 + 33*x^25 + 90*x^24 + 22*x^23 + 72*x^22 + 78*x^21 + 20*x^20 + 19*x^19 + 104*x^18 + 27*x^17 + 102*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 70*x^8 + 70*x^7 + 40*x^6 + 94*x^5 + 20*x^4 + 117*x^3 + 8*x^2 + 29*x + 58, x^27 + 33*x^25 + 14*x^24 + 38*x^23 + 88*x^22 + 126*x^21 + 92*x^20 + 67*x^19 + 120*x^18 + 43*x^17 + 82*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 18*x^8 + 22*x^7 + 120*x^6 + 78*x^5 + 92*x^4 + 101*x^3 + 88*x^2 + 109*x + 78, x^27 + 33*x^25 + 126*x^24 + 6*x^23 + 120*x^22 + 94*x^21 + 28*x^20 + 99*x^19 + 88*x^18 + 75*x^17 + 2*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 98*x^8 + 118*x^7 + 24*x^6 + 46*x^5 + 28*x^4 + 5*x^3 + 56*x^2 + 13*x + 94, x^27 + 33*x^25 + 30*x^24 + 22*x^23 + 8*x^22 + 46*x^21 + 108*x^20 + 83*x^19 + 72*x^18 + 123*x^17 + 82*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 34*x^8 + 70*x^7 + 104*x^6 + 62*x^5 + 44*x^4 + 53*x^3 + 104*x^2 + 125*x + 46, x^27 + 33*x^25 + 102*x^24 + 38*x^23 + 40*x^22 + 94*x^21 + 28*x^20 + 3*x^19 + 40*x^18 + 11*x^17 + 42*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 26*x^8 + 22*x^7 + 8*x^6 + 46*x^5 + 92*x^4 + 37*x^3 + 72*x^2 + 77*x + 22, x^27 + 33*x^25 + 54*x^24 + 54*x^23 + 24*x^22 + 46*x^21 + 108*x^20 + 115*x^19 + 56*x^18 + 59*x^17 + 42*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 106*x^8 + 102*x^7 + 56*x^6 + 62*x^5 + 108*x^4 + 85*x^3 + 24*x^2 + 61*x + 118, x^27 + 33*x^25 + 30*x^24 + 118*x^23 + 72*x^22 + 14*x^21 + 44*x^20 + 115*x^19 + 8*x^18 + 27*x^17 + 18*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 34*x^8 + 38*x^7 + 40*x^6 + 30*x^5 + 108*x^4 + 85*x^3 + 40*x^2 + 29*x + 110, x^27 + 33*x^25 + 54*x^24 + 38*x^23 + 8*x^22 + 94*x^21 + 92*x^20 + 3*x^19 + 72*x^18 + 11*x^17 + 58*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 10*x^8 + 22*x^7 + 104*x^6 + 46*x^5 + 28*x^4 + 37*x^3 + 104*x^2 + 77*x + 70, x^27 + 33*x^25 + 106*x^24 + 22*x^23 + 72*x^22 + 78*x^21 + 116*x^20 + 19*x^19 + 104*x^18 + 27*x^17 + 22*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 54*x^8 + 70*x^7 + 40*x^6 + 94*x^5 + 116*x^4 + 117*x^3 + 8*x^2 + 29*x + 10, x^27 + 33*x^25 + 22*x^24 + 54*x^23 + 88*x^22 + 46*x^21 + 108*x^20 + 115*x^19 + 120*x^18 + 59*x^17 + 10*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 10*x^8 + 102*x^7 + 120*x^6 + 62*x^5 + 108*x^4 + 85*x^3 + 88*x^2 + 61*x + 22, x^27 + 33*x^25 + 86*x^24 + 38*x^23 + 72*x^22 + 94*x^21 + 92*x^20 + 3*x^19 + 8*x^18 + 11*x^17 + 90*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 106*x^8 + 22*x^7 + 40*x^6 + 46*x^5 + 28*x^4 + 37*x^3 + 40*x^2 + 77*x + 38, x^27 + 33*x^25 + 30*x^24 + 54*x^23 + 104*x^22 + 78*x^21 + 76*x^20 + 51*x^19 + 104*x^18 + 91*x^17 + 114*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 98*x^8 + 102*x^7 + 72*x^6 + 94*x^5 + 12*x^4 + 21*x^3 + 8*x^2 + 93*x + 78, x^27 + 33*x^25 + 22*x^24 + 86*x^23 + 88*x^22 + 78*x^21 + 108*x^20 + 83*x^19 + 120*x^18 + 27*x^17 + 10*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 10*x^8 + 6*x^7 + 120*x^6 + 94*x^5 + 108*x^4 + 53*x^3 + 88*x^2 + 29*x + 22, x^27 + 33*x^25 + 66*x^24 + 70*x^23 + 104*x^22 + 94*x^21 + 4*x^20 + 35*x^19 + 72*x^18 + 75*x^17 + 30*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 30*x^8 + 54*x^7 + 72*x^6 + 46*x^5 + 4*x^4 + 69*x^3 + 104*x^2 + 13*x + 66, x^27 + 33*x^25 + 46*x^24 + 86*x^23 + 104*x^22 + 110*x^21 + 44*x^20 + 19*x^19 + 104*x^18 + 59*x^17 + 34*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 82*x^8 + 6*x^7 + 72*x^6 + 126*x^5 + 108*x^4 + 117*x^3 + 8*x^2 + 61*x + 30, x^27 + 33*x^25 + 14*x^24 + 22*x^23 + 104*x^22 + 110*x^21 + 44*x^20 + 83*x^19 + 104*x^18 + 59*x^17 + 2*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 114*x^8 + 70*x^7 + 72*x^6 + 126*x^5 + 108*x^4 + 53*x^3 + 8*x^2 + 61*x + 62, x^27 + 33*x^25 + 54*x^24 + 70*x^23 + 104*x^22 + 62*x^21 + 124*x^20 + 99*x^19 + 104*x^18 + 43*x^17 + 26*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 74*x^8 + 54*x^7 + 72*x^6 + 14*x^5 + 60*x^4 + 5*x^3 + 8*x^2 + 109*x + 38, x^27 + 33*x^25 + 18*x^24 + 86*x^23 + 56*x^22 + 46*x^21 + 52*x^20 + 19*x^19 + 120*x^18 + 123*x^17 + 62*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 46*x^8 + 6*x^7 + 88*x^6 + 62*x^5 + 116*x^4 + 117*x^3 + 88*x^2 + 125*x + 66, x^27 + 33*x^25 + 54*x^24 + 118*x^23 + 56*x^22 + 46*x^21 + 76*x^20 + 51*x^19 + 24*x^18 + 59*x^17 + 74*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 42*x^8 + 38*x^7 + 88*x^6 + 62*x^5 + 76*x^4 + 21*x^3 + 120*x^2 + 61*x + 22, x^27 + 33*x^25 + 30*x^24 + 54*x^23 + 104*x^22 + 14*x^21 + 12*x^20 + 51*x^19 + 104*x^18 + 27*x^17 + 50*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 98*x^8 + 102*x^7 + 72*x^6 + 30*x^5 + 76*x^4 + 21*x^3 + 8*x^2 + 29*x + 14, x^27 + 33*x^25 + 46*x^24 + 118*x^23 + 104*x^22 + 78*x^21 + 108*x^20 + 115*x^19 + 104*x^18 + 91*x^17 + 98*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 82*x^8 + 38*x^7 + 72*x^6 + 94*x^5 + 44*x^4 + 85*x^3 + 8*x^2 + 93*x + 94, x^27 + 33*x^25 + 70*x^24 + 118*x^23 + 120*x^22 + 110*x^21 + 44*x^20 + 51*x^19 + 88*x^18 + 123*x^17 + 122*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 26*x^8 + 38*x^7 + 24*x^6 + 126*x^5 + 44*x^4 + 21*x^3 + 56*x^2 + 125*x + 102, x^27 + 33*x^25 + 6*x^24 + 70*x^23 + 72*x^22 + 126*x^21 + 124*x^20 + 99*x^19 + 8*x^18 + 107*x^17 + 106*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 58*x^8 + 54*x^7 + 40*x^6 + 78*x^5 + 60*x^4 + 5*x^3 + 40*x^2 + 45*x + 22, x^27 + 33*x^25 + 94*x^24 + 86*x^23 + 8*x^22 + 110*x^21 + 108*x^20 + 19*x^19 + 72*x^18 + 59*x^17 + 18*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 98*x^8 + 6*x^7 + 104*x^6 + 126*x^5 + 44*x^4 + 117*x^3 + 104*x^2 + 61*x + 110, x^27 + 33*x^25 + 10*x^24 + 118*x^23 + 8*x^22 + 46*x^21 + 116*x^20 + 51*x^19 + 40*x^18 + 59*x^17 + 54*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 22*x^8 + 38*x^7 + 104*x^6 + 62*x^5 + 116*x^4 + 21*x^3 + 72*x^2 + 61*x + 106, x^27 + 33*x^25 + 18*x^24 + 118*x^23 + 24*x^22 + 14*x^21 + 84*x^20 + 115*x^19 + 24*x^18 + 27*x^17 + 30*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 110*x^8 + 38*x^7 + 56*x^6 + 30*x^5 + 20*x^4 + 85*x^3 + 120*x^2 + 29*x + 34, x^27 + 33*x^25 + 58*x^24 + 6*x^23 + 88*x^22 + 62*x^21 + 36*x^20 + 35*x^19 + 88*x^18 + 43*x^17 + 54*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 70*x^8 + 118*x^7 + 120*x^6 + 14*x^5 + 100*x^4 + 69*x^3 + 56*x^2 + 109*x + 10, x^27 + 33*x^25 + 82*x^24 + 6*x^23 + 8*x^22 + 30*x^21 + 4*x^20 + 99*x^19 + 40*x^18 + 11*x^17 + 46*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 78*x^8 + 118*x^7 + 104*x^6 + 110*x^5 + 4*x^4 + 5*x^3 + 72*x^2 + 77*x + 114, x^27 + 33*x^25 + 58*x^24 + 118*x^23 + 8*x^22 + 46*x^21 + 20*x^20 + 51*x^19 + 40*x^18 + 59*x^17 + 70*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 102*x^8 + 38*x^7 + 104*x^6 + 62*x^5 + 20*x^4 + 21*x^3 + 72*x^2 + 61*x + 90, x^27 + 33*x^25 + 14*x^24 + 70*x^23 + 24*x^22 + 30*x^21 + 28*x^20 + 35*x^19 + 56*x^18 + 11*x^17 + 18*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 18*x^8 + 54*x^7 + 56*x^6 + 110*x^5 + 28*x^4 + 69*x^3 + 24*x^2 + 77*x + 14, x^27 + 33*x^25 + 38*x^24 + 38*x^23 + 104*x^22 + 30*x^21 + 28*x^20 + 3*x^19 + 104*x^18 + 75*x^17 + 106*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 90*x^8 + 22*x^7 + 72*x^6 + 110*x^5 + 92*x^4 + 37*x^3 + 8*x^2 + 13*x + 86, x^27 + 33*x^25 + 122*x^24 + 86*x^23 + 104*x^22 + 14*x^21 + 116*x^20 + 83*x^19 + 72*x^18 + 91*x^17 + 38*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 102*x^8 + 6*x^7 + 72*x^6 + 30*x^5 + 116*x^4 + 53*x^3 + 104*x^2 + 93*x + 58, x^27 + 33*x^25 + 86*x^24 + 70*x^23 + 40*x^22 + 62*x^21 + 124*x^20 + 99*x^19 + 40*x^18 + 43*x^17 + 58*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 42*x^8 + 54*x^7 + 8*x^6 + 14*x^5 + 60*x^4 + 5*x^3 + 72*x^2 + 109*x + 6, x^27 + 33*x^25 + 62*x^24 + 86*x^23 + 40*x^22 + 46*x^21 + 12*x^20 + 19*x^19 + 40*x^18 + 123*x^17 + 82*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 66*x^8 + 6*x^7 + 8*x^6 + 62*x^5 + 76*x^4 + 117*x^3 + 72*x^2 + 125*x + 110, x^27 + 33*x^25 + 86*x^24 + 22*x^23 + 88*x^22 + 14*x^21 + 108*x^20 + 19*x^19 + 120*x^18 + 91*x^17 + 74*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 74*x^8 + 70*x^7 + 120*x^6 + 30*x^5 + 108*x^4 + 117*x^3 + 88*x^2 + 93*x + 86, x^27 + 33*x^25 + 66*x^24 + 22*x^23 + 24*x^22 + 110*x^21 + 52*x^20 + 83*x^19 + 24*x^18 + 59*x^17 + 110*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 62*x^8 + 70*x^7 + 56*x^6 + 126*x^5 + 116*x^4 + 53*x^3 + 120*x^2 + 61*x + 82, x^27 + 33*x^25 + 62*x^24 + 70*x^23 + 24*x^22 + 30*x^21 + 60*x^20 + 35*x^19 + 56*x^18 + 11*x^17 + 34*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 98*x^8 + 54*x^7 + 56*x^6 + 110*x^5 + 60*x^4 + 69*x^3 + 24*x^2 + 77*x + 126, x^27 + 33*x^25 + 26*x^24 + 102*x^23 + 120*x^22 + 30*x^21 + 4*x^20 + 67*x^19 + 56*x^18 + 75*x^17 + 54*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 38*x^8 + 86*x^7 + 24*x^6 + 110*x^5 + 68*x^4 + 101*x^3 + 24*x^2 + 13*x + 74, x^27 + 33*x^25 + 38*x^24 + 86*x^23 + 24*x^22 + 14*x^21 + 76*x^20 + 83*x^19 + 56*x^18 + 91*x^17 + 58*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 122*x^8 + 6*x^7 + 56*x^6 + 30*x^5 + 76*x^4 + 53*x^3 + 24*x^2 + 93*x + 102, x^27 + 33*x^25 + 94*x^24 + 70*x^23 + 24*x^22 + 30*x^21 + 124*x^20 + 35*x^19 + 56*x^18 + 11*x^17 + 2*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 66*x^8 + 54*x^7 + 56*x^6 + 110*x^5 + 124*x^4 + 69*x^3 + 24*x^2 + 77*x + 30, x^27 + 33*x^25 + 26*x^24 + 22*x^23 + 72*x^22 + 14*x^21 + 84*x^20 + 19*x^19 + 104*x^18 + 91*x^17 + 102*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 6*x^8 + 70*x^7 + 40*x^6 + 30*x^5 + 84*x^4 + 117*x^3 + 8*x^2 + 93*x + 58, x^27 + 33*x^25 + 114*x^24 + 38*x^23 + 72*x^22 + 126*x^21 + 68*x^20 + 67*x^19 + 104*x^18 + 43*x^17 + 14*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 46*x^8 + 22*x^7 + 40*x^6 + 78*x^5 + 68*x^4 + 101*x^3 + 8*x^2 + 109*x + 18, x^27 + 33*x^25 + 42*x^24 + 38*x^23 + 56*x^22 + 94*x^21 + 36*x^20 + 3*x^19 + 120*x^18 + 11*x^17 + 38*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 22*x^8 + 22*x^7 + 88*x^6 + 46*x^5 + 100*x^4 + 37*x^3 + 88*x^2 + 77*x + 90, x^27 + 33*x^25 + 114*x^24 + 118*x^23 + 120*x^22 + 14*x^21 + 116*x^20 + 115*x^19 + 56*x^18 + 27*x^17 + 94*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 78*x^8 + 38*x^7 + 24*x^6 + 30*x^5 + 52*x^4 + 85*x^3 + 24*x^2 + 29*x + 34, x^27 + 33*x^25 + 106*x^24 + 6*x^23 + 56*x^22 + 126*x^21 + 100*x^20 + 35*x^19 + 120*x^18 + 107*x^17 + 38*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 86*x^8 + 118*x^7 + 88*x^6 + 78*x^5 + 36*x^4 + 69*x^3 + 88*x^2 + 45*x + 90, x^27 + 33*x^25 + 10*x^24 + 102*x^23 + 56*x^22 + 94*x^21 + 36*x^20 + 67*x^19 + 120*x^18 + 11*x^17 + 6*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 54*x^8 + 86*x^7 + 88*x^6 + 46*x^5 + 100*x^4 + 101*x^3 + 88*x^2 + 77*x + 122, x^27 + 33*x^25 + 30*x^24 + 86*x^23 + 104*x^22 + 46*x^21 + 12*x^20 + 19*x^19 + 104*x^18 + 123*x^17 + 50*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 98*x^8 + 6*x^7 + 72*x^6 + 62*x^5 + 76*x^4 + 117*x^3 + 8*x^2 + 125*x + 14, x^27 + 33*x^25 + 14*x^24 + 70*x^23 + 88*x^22 + 94*x^21 + 28*x^20 + 35*x^19 + 120*x^18 + 75*x^17 + 18*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 18*x^8 + 54*x^7 + 120*x^6 + 46*x^5 + 28*x^4 + 69*x^3 + 88*x^2 + 13*x + 14, x^27 + 33*x^25 + 34*x^24 + 70*x^23 + 8*x^22 + 94*x^21 + 100*x^20 + 35*x^19 + 40*x^18 + 75*x^17 + 30*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 126*x^8 + 54*x^7 + 104*x^6 + 46*x^5 + 100*x^4 + 69*x^3 + 72*x^2 + 13*x + 2, x^27 + 33*x^25 + 38*x^24 + 118*x^23 + 120*x^22 + 46*x^21 + 44*x^20 + 51*x^19 + 88*x^18 + 59*x^17 + 90*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 58*x^8 + 38*x^7 + 24*x^6 + 62*x^5 + 44*x^4 + 21*x^3 + 56*x^2 + 61*x + 6, x^27 + 33*x^25 + 10*x^24 + 22*x^23 + 104*x^22 + 14*x^21 + 20*x^20 + 19*x^19 + 72*x^18 + 91*x^17 + 22*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 86*x^8 + 70*x^7 + 72*x^6 + 30*x^5 + 20*x^4 + 117*x^3 + 104*x^2 + 93*x + 74, x^27 + 33*x^25 + 58*x^24 + 22*x^23 + 40*x^22 + 14*x^21 + 116*x^20 + 19*x^19 + 8*x^18 + 91*x^17 + 102*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 38*x^8 + 70*x^7 + 8*x^6 + 30*x^5 + 116*x^4 + 117*x^3 + 40*x^2 + 93*x + 122, x^27 + 33*x^25 + 126*x^24 + 118*x^23 + 72*x^22 + 14*x^21 + 108*x^20 + 115*x^19 + 8*x^18 + 27*x^17 + 50*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 66*x^8 + 38*x^7 + 40*x^6 + 30*x^5 + 44*x^4 + 85*x^3 + 40*x^2 + 29*x + 78, x^27 + 33*x^25 + 74*x^24 + 102*x^23 + 120*x^22 + 30*x^21 + 36*x^20 + 67*x^19 + 56*x^18 + 75*x^17 + 70*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 118*x^8 + 86*x^7 + 24*x^6 + 110*x^5 + 100*x^4 + 101*x^3 + 24*x^2 + 13*x + 58, x^27 + 33*x^25 + 58*x^24 + 6*x^23 + 56*x^22 + 62*x^21 + 4*x^20 + 35*x^19 + 120*x^18 + 43*x^17 + 86*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 6*x^8 + 118*x^7 + 88*x^6 + 14*x^5 + 68*x^4 + 69*x^3 + 88*x^2 + 109*x + 42, x^27 + 33*x^25 + 78*x^24 + 102*x^23 + 56*x^22 + 126*x^21 + 124*x^20 + 3*x^19 + 24*x^18 + 43*x^17 + 114*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 18*x^8 + 86*x^7 + 88*x^6 + 78*x^5 + 124*x^4 + 37*x^3 + 120*x^2 + 109*x + 110, x^27 + 33*x^25 + 126*x^24 + 22*x^23 + 40*x^22 + 110*x^21 + 12*x^20 + 83*x^19 + 40*x^18 + 59*x^17 + 18*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 2*x^8 + 70*x^7 + 8*x^6 + 126*x^5 + 76*x^4 + 53*x^3 + 72*x^2 + 61*x + 46, x^27 + 33*x^25 + 70*x^24 + 102*x^23 + 8*x^22 + 94*x^21 + 124*x^20 + 67*x^19 + 72*x^18 + 11*x^17 + 42*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 122*x^8 + 86*x^7 + 104*x^6 + 46*x^5 + 60*x^4 + 101*x^3 + 104*x^2 + 77*x + 86, x^27 + 33*x^25 + 110*x^24 + 102*x^23 + 56*x^22 + 126*x^21 + 60*x^20 + 3*x^19 + 24*x^18 + 43*x^17 + 82*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 114*x^8 + 86*x^7 + 88*x^6 + 78*x^5 + 60*x^4 + 37*x^3 + 120*x^2 + 109*x + 14, x^27 + 33*x^25 + 118*x^24 + 70*x^23 + 40*x^22 + 62*x^21 + 60*x^20 + 99*x^19 + 40*x^18 + 43*x^17 + 26*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 10*x^8 + 54*x^7 + 8*x^6 + 14*x^5 + 124*x^4 + 5*x^3 + 72*x^2 + 109*x + 38, x^27 + 33*x^25 + 50*x^24 + 118*x^23 + 56*x^22 + 78*x^21 + 116*x^20 + 115*x^19 + 120*x^18 + 91*x^17 + 30*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 14*x^8 + 38*x^7 + 88*x^6 + 94*x^5 + 52*x^4 + 85*x^3 + 88*x^2 + 93*x + 98, x^27 + 33*x^25 + 82*x^24 + 38*x^23 + 104*x^22 + 126*x^21 + 36*x^20 + 67*x^19 + 72*x^18 + 43*x^17 + 14*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 14*x^8 + 22*x^7 + 72*x^6 + 78*x^5 + 36*x^4 + 101*x^3 + 104*x^2 + 109*x + 82, x^27 + 33*x^25 + 114*x^24 + 118*x^23 + 24*x^22 + 78*x^21 + 84*x^20 + 115*x^19 + 24*x^18 + 91*x^17 + 126*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 14*x^8 + 38*x^7 + 56*x^6 + 94*x^5 + 20*x^4 + 85*x^3 + 120*x^2 + 93*x + 66, x^27 + 33*x^25 + 86*x^24 + 86*x^23 + 88*x^22 + 78*x^21 + 108*x^20 + 83*x^19 + 120*x^18 + 27*x^17 + 74*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 74*x^8 + 6*x^7 + 120*x^6 + 94*x^5 + 108*x^4 + 53*x^3 + 88*x^2 + 29*x + 86, x^27 + 33*x^25 + 106*x^24 + 22*x^23 + 8*x^22 + 14*x^21 + 116*x^20 + 19*x^19 + 40*x^18 + 91*x^17 + 22*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 54*x^8 + 70*x^7 + 104*x^6 + 30*x^5 + 116*x^4 + 117*x^3 + 72*x^2 + 93*x + 10, x^27 + 33*x^25 + 122*x^24 + 70*x^23 + 88*x^22 + 62*x^21 + 100*x^20 + 99*x^19 + 88*x^18 + 43*x^17 + 54*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 6*x^8 + 54*x^7 + 120*x^6 + 14*x^5 + 36*x^4 + 5*x^3 + 56*x^2 + 109*x + 10, x^27 + 33*x^25 + 86*x^24 + 54*x^23 + 88*x^22 + 46*x^21 + 108*x^20 + 115*x^19 + 120*x^18 + 59*x^17 + 74*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 74*x^8 + 102*x^7 + 120*x^6 + 62*x^5 + 108*x^4 + 85*x^3 + 88*x^2 + 61*x + 86, x^27 + 33*x^25 + 42*x^24 + 38*x^23 + 24*x^22 + 30*x^21 + 68*x^20 + 3*x^19 + 24*x^18 + 75*x^17 + 6*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 86*x^8 + 22*x^7 + 56*x^6 + 110*x^5 + 4*x^4 + 37*x^3 + 120*x^2 + 13*x + 58, x^27 + 33*x^25 + 6*x^24 + 86*x^23 + 120*x^22 + 14*x^21 + 108*x^20 + 83*x^19 + 88*x^18 + 91*x^17 + 122*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 90*x^8 + 6*x^7 + 24*x^6 + 30*x^5 + 108*x^4 + 53*x^3 + 56*x^2 + 93*x + 102, x^27 + 33*x^25 + 58*x^24 + 118*x^23 + 104*x^22 + 46*x^21 + 116*x^20 + 51*x^19 + 72*x^18 + 59*x^17 + 102*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 38*x^8 + 38*x^7 + 72*x^6 + 62*x^5 + 116*x^4 + 21*x^3 + 104*x^2 + 61*x + 122, x^27 + 33*x^25 + 10*x^24 + 38*x^23 + 56*x^22 + 94*x^21 + 100*x^20 + 3*x^19 + 120*x^18 + 11*x^17 + 70*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 54*x^8 + 22*x^7 + 88*x^6 + 46*x^5 + 36*x^4 + 37*x^3 + 88*x^2 + 77*x + 58, x^27 + 33*x^25 + 98*x^24 + 22*x^23 + 88*x^22 + 46*x^21 + 116*x^20 + 83*x^19 + 88*x^18 + 123*x^17 + 78*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 30*x^8 + 70*x^7 + 120*x^6 + 62*x^5 + 52*x^4 + 53*x^3 + 56*x^2 + 125*x + 114, x^27 + 33*x^25 + 34*x^24 + 54*x^23 + 120*x^22 + 14*x^21 + 84*x^20 + 51*x^19 + 56*x^18 + 27*x^17 + 46*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 30*x^8 + 102*x^7 + 24*x^6 + 30*x^5 + 20*x^4 + 21*x^3 + 24*x^2 + 29*x + 82, x^27 + 33*x^25 + 74*x^24 + 54*x^23 + 40*x^22 + 110*x^21 + 20*x^20 + 115*x^19 + 8*x^18 + 123*x^17 + 86*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 22*x^8 + 102*x^7 + 8*x^6 + 126*x^5 + 20*x^4 + 85*x^3 + 40*x^2 + 125*x + 10, x^27 + 33*x^25 + 118*x^24 + 38*x^23 + 72*x^22 + 94*x^21 + 28*x^20 + 3*x^19 + 8*x^18 + 11*x^17 + 58*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 74*x^8 + 22*x^7 + 40*x^6 + 46*x^5 + 92*x^4 + 37*x^3 + 40*x^2 + 77*x + 70, x^27 + 33*x^25 + 94*x^24 + 6*x^23 + 56*x^22 + 94*x^21 + 28*x^20 + 99*x^19 + 24*x^18 + 75*x^17 + 98*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 2*x^8 + 118*x^7 + 88*x^6 + 46*x^5 + 28*x^4 + 5*x^3 + 120*x^2 + 13*x + 126, x^27 + 33*x^25 + 122*x^24 + 54*x^23 + 40*x^22 + 46*x^21 + 116*x^20 + 115*x^19 + 8*x^18 + 59*x^17 + 38*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 102*x^8 + 102*x^7 + 8*x^6 + 62*x^5 + 116*x^4 + 85*x^3 + 40*x^2 + 61*x + 58, x^27 + 33*x^25 + 74*x^24 + 70*x^23 + 120*x^22 + 62*x^21 + 100*x^20 + 99*x^19 + 56*x^18 + 43*x^17 + 6*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 118*x^8 + 54*x^7 + 24*x^6 + 14*x^5 + 36*x^4 + 5*x^3 + 24*x^2 + 109*x + 122, x^27 + 33*x^25 + 78*x^24 + 6*x^23 + 56*x^22 + 94*x^21 + 60*x^20 + 99*x^19 + 24*x^18 + 75*x^17 + 50*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 18*x^8 + 118*x^7 + 88*x^6 + 46*x^5 + 60*x^4 + 5*x^3 + 120*x^2 + 13*x + 46, x^27 + 33*x^25 + 34*x^24 + 22*x^23 + 88*x^22 + 46*x^21 + 116*x^20 + 83*x^19 + 88*x^18 + 123*x^17 + 14*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 94*x^8 + 70*x^7 + 120*x^6 + 62*x^5 + 52*x^4 + 53*x^3 + 56*x^2 + 125*x + 50, x^27 + 33*x^25 + 6*x^24 + 22*x^23 + 88*x^22 + 78*x^21 + 76*x^20 + 19*x^19 + 120*x^18 + 27*x^17 + 26*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 26*x^8 + 70*x^7 + 120*x^6 + 94*x^5 + 76*x^4 + 117*x^3 + 88*x^2 + 29*x + 6, x^27 + 33*x^25 + 110*x^24 + 6*x^23 + 56*x^22 + 30*x^21 + 60*x^20 + 99*x^19 + 24*x^18 + 11*x^17 + 82*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 114*x^8 + 118*x^7 + 88*x^6 + 110*x^5 + 60*x^4 + 5*x^3 + 120*x^2 + 77*x + 14, x^27 + 33*x^25 + 10*x^24 + 86*x^23 + 104*x^22 + 78*x^21 + 20*x^20 + 83*x^19 + 72*x^18 + 27*x^17 + 22*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 86*x^8 + 6*x^7 + 72*x^6 + 94*x^5 + 20*x^4 + 53*x^3 + 104*x^2 + 29*x + 74, x^27 + 33*x^25 + 70*x^24 + 86*x^23 + 24*x^22 + 14*x^21 + 12*x^20 + 83*x^19 + 56*x^18 + 91*x^17 + 26*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 90*x^8 + 6*x^7 + 56*x^6 + 30*x^5 + 12*x^4 + 53*x^3 + 24*x^2 + 93*x + 6, x^27 + 33*x^25 + 14*x^24 + 38*x^23 + 120*x^22 + 126*x^21 + 124*x^20 + 67*x^19 + 88*x^18 + 43*x^17 + 50*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 82*x^8 + 22*x^7 + 24*x^6 + 78*x^5 + 124*x^4 + 101*x^3 + 56*x^2 + 109*x + 46, x^27 + 33*x^25 + 58*x^24 + 86*x^23 + 40*x^22 + 78*x^21 + 116*x^20 + 83*x^19 + 8*x^18 + 27*x^17 + 102*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 38*x^8 + 6*x^7 + 8*x^6 + 94*x^5 + 116*x^4 + 53*x^3 + 40*x^2 + 29*x + 122, x^27 + 33*x^25 + 34*x^24 + 70*x^23 + 104*x^22 + 94*x^21 + 68*x^20 + 35*x^19 + 72*x^18 + 75*x^17 + 62*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 62*x^8 + 54*x^7 + 72*x^6 + 46*x^5 + 68*x^4 + 69*x^3 + 104*x^2 + 13*x + 34, x^27 + 33*x^25 + 18*x^24 + 22*x^23 + 24*x^22 + 46*x^21 + 84*x^20 + 83*x^19 + 24*x^18 + 123*x^17 + 30*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 110*x^8 + 70*x^7 + 56*x^6 + 62*x^5 + 20*x^4 + 53*x^3 + 120*x^2 + 125*x + 34, x^27 + 33*x^25 + 14*x^24 + 102*x^23 + 120*x^22 + 62*x^21 + 124*x^20 + 3*x^19 + 88*x^18 + 107*x^17 + 50*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 82*x^8 + 86*x^7 + 24*x^6 + 14*x^5 + 124*x^4 + 37*x^3 + 56*x^2 + 45*x + 46, x^27 + 33*x^25 + 34*x^24 + 102*x^23 + 72*x^22 + 126*x^21 + 36*x^20 + 3*x^19 + 104*x^18 + 43*x^17 + 94*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 126*x^8 + 86*x^7 + 40*x^6 + 78*x^5 + 36*x^4 + 37*x^3 + 8*x^2 + 109*x + 66, x^27 + 33*x^25 + 78*x^24 + 86*x^23 + 104*x^22 + 110*x^21 + 108*x^20 + 19*x^19 + 104*x^18 + 59*x^17 + 2*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 50*x^8 + 6*x^7 + 72*x^6 + 126*x^5 + 44*x^4 + 117*x^3 + 8*x^2 + 61*x + 62, x^27 + 33*x^25 + 30*x^24 + 22*x^23 + 40*x^22 + 110*x^21 + 76*x^20 + 83*x^19 + 40*x^18 + 59*x^17 + 114*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 98*x^8 + 70*x^7 + 8*x^6 + 126*x^5 + 12*x^4 + 53*x^3 + 72*x^2 + 61*x + 78, x^27 + 33*x^25 + 82*x^24 + 6*x^23 + 72*x^22 + 30*x^21 + 68*x^20 + 99*x^19 + 104*x^18 + 11*x^17 + 110*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 78*x^8 + 118*x^7 + 40*x^6 + 110*x^5 + 68*x^4 + 5*x^3 + 8*x^2 + 77*x + 50, x^27 + 33*x^25 + 54*x^24 + 22*x^23 + 88*x^22 + 78*x^21 + 108*x^20 + 19*x^19 + 120*x^18 + 27*x^17 + 42*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 106*x^8 + 70*x^7 + 120*x^6 + 94*x^5 + 108*x^4 + 117*x^3 + 88*x^2 + 29*x + 118, x^27 + 33*x^25 + 34*x^24 + 54*x^23 + 120*x^22 + 78*x^21 + 20*x^20 + 51*x^19 + 56*x^18 + 91*x^17 + 110*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 30*x^8 + 102*x^7 + 24*x^6 + 94*x^5 + 84*x^4 + 21*x^3 + 24*x^2 + 93*x + 18, x^27 + 33*x^25 + 70*x^24 + 22*x^23 + 88*x^22 + 78*x^21 + 76*x^20 + 19*x^19 + 120*x^18 + 27*x^17 + 90*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 90*x^8 + 70*x^7 + 120*x^6 + 94*x^5 + 76*x^4 + 117*x^3 + 88*x^2 + 29*x + 70, x^27 + 33*x^25 + 94*x^24 + 22*x^23 + 8*x^22 + 110*x^21 + 44*x^20 + 83*x^19 + 72*x^18 + 59*x^17 + 82*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 98*x^8 + 70*x^7 + 104*x^6 + 126*x^5 + 108*x^4 + 53*x^3 + 104*x^2 + 61*x + 46, x^27 + 33*x^25 + 2*x^24 + 70*x^23 + 72*x^22 + 94*x^21 + 100*x^20 + 35*x^19 + 104*x^18 + 75*x^17 + 126*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 30*x^8 + 54*x^7 + 40*x^6 + 46*x^5 + 100*x^4 + 69*x^3 + 8*x^2 + 13*x + 34, x^27 + 33*x^25 + 46*x^24 + 102*x^23 + 120*x^22 + 62*x^21 + 60*x^20 + 3*x^19 + 88*x^18 + 107*x^17 + 18*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 50*x^8 + 86*x^7 + 24*x^6 + 14*x^5 + 60*x^4 + 37*x^3 + 56*x^2 + 45*x + 78, x^27 + 33*x^25 + 122*x^24 + 6*x^23 + 24*x^22 + 126*x^21 + 36*x^20 + 35*x^19 + 24*x^18 + 107*x^17 + 118*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 6*x^8 + 118*x^7 + 56*x^6 + 78*x^5 + 100*x^4 + 69*x^3 + 120*x^2 + 45*x + 74, x^27 + 33*x^25 + 14*x^24 + 118*x^23 + 40*x^22 + 14*x^21 + 44*x^20 + 115*x^19 + 40*x^18 + 27*x^17 + 2*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 114*x^8 + 38*x^7 + 8*x^6 + 30*x^5 + 108*x^4 + 85*x^3 + 72*x^2 + 29*x + 62, x^27 + 33*x^25 + 118*x^24 + 86*x^23 + 24*x^22 + 78*x^21 + 108*x^20 + 83*x^19 + 56*x^18 + 27*x^17 + 106*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 42*x^8 + 6*x^7 + 56*x^6 + 94*x^5 + 108*x^4 + 53*x^3 + 24*x^2 + 29*x + 54, x^27 + 33*x^25 + 90*x^24 + 86*x^23 + 104*x^22 + 14*x^21 + 52*x^20 + 83*x^19 + 72*x^18 + 91*x^17 + 70*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 6*x^8 + 6*x^7 + 72*x^6 + 30*x^5 + 52*x^4 + 53*x^3 + 104*x^2 + 93*x + 26, x^27 + 33*x^25 + 54*x^24 + 102*x^23 + 40*x^22 + 30*x^21 + 124*x^20 + 67*x^19 + 40*x^18 + 75*x^17 + 26*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 74*x^8 + 86*x^7 + 8*x^6 + 110*x^5 + 60*x^4 + 101*x^3 + 72*x^2 + 13*x + 38, x^27 + 33*x^25 + 34*x^24 + 70*x^23 + 40*x^22 + 30*x^21 + 68*x^20 + 35*x^19 + 8*x^18 + 11*x^17 + 62*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 62*x^8 + 54*x^7 + 8*x^6 + 110*x^5 + 68*x^4 + 69*x^3 + 40*x^2 + 77*x + 34, x^27 + 33*x^25 + 18*x^24 + 102*x^23 + 104*x^22 + 62*x^21 + 36*x^20 + 3*x^19 + 72*x^18 + 107*x^17 + 78*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 78*x^8 + 86*x^7 + 72*x^6 + 14*x^5 + 36*x^4 + 37*x^3 + 104*x^2 + 45*x + 18, x^27 + 33*x^25 + 50*x^24 + 86*x^23 + 56*x^22 + 46*x^21 + 116*x^20 + 19*x^19 + 120*x^18 + 123*x^17 + 30*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 14*x^8 + 6*x^7 + 88*x^6 + 62*x^5 + 52*x^4 + 117*x^3 + 88*x^2 + 125*x + 98, x^27 + 33*x^25 + 62*x^24 + 38*x^23 + 24*x^22 + 62*x^21 + 124*x^20 + 67*x^19 + 56*x^18 + 107*x^17 + 98*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 98*x^8 + 22*x^7 + 56*x^6 + 14*x^5 + 124*x^4 + 101*x^3 + 24*x^2 + 45*x + 62, x^27 + 33*x^25 + 122*x^24 + 38*x^23 + 88*x^22 + 94*x^21 + 36*x^20 + 3*x^19 + 88*x^18 + 11*x^17 + 118*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 6*x^8 + 22*x^7 + 120*x^6 + 46*x^5 + 100*x^4 + 37*x^3 + 56*x^2 + 77*x + 74, x^27 + 33*x^25 + 22*x^24 + 6*x^23 + 40*x^22 + 126*x^21 + 124*x^20 + 35*x^19 + 40*x^18 + 107*x^17 + 122*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 106*x^8 + 118*x^7 + 8*x^6 + 78*x^5 + 60*x^4 + 69*x^3 + 72*x^2 + 45*x + 70, x^27 + 33*x^25 + 114*x^24 + 70*x^23 + 40*x^22 + 30*x^21 + 36*x^20 + 35*x^19 + 8*x^18 + 11*x^17 + 46*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 110*x^8 + 54*x^7 + 8*x^6 + 110*x^5 + 36*x^4 + 69*x^3 + 40*x^2 + 77*x + 50, x^27 + 33*x^25 + 62*x^24 + 6*x^23 + 56*x^22 + 30*x^21 + 28*x^20 + 99*x^19 + 24*x^18 + 11*x^17 + 66*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 34*x^8 + 118*x^7 + 88*x^6 + 110*x^5 + 28*x^4 + 5*x^3 + 120*x^2 + 77*x + 30, x^27 + 33*x^25 + 102*x^24 + 38*x^23 + 72*x^22 + 94*x^21 + 60*x^20 + 3*x^19 + 8*x^18 + 11*x^17 + 10*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 90*x^8 + 22*x^7 + 40*x^6 + 46*x^5 + 124*x^4 + 37*x^3 + 40*x^2 + 77*x + 118, x^27 + 33*x^25 + 54*x^24 + 22*x^23 + 120*x^22 + 14*x^21 + 76*x^20 + 19*x^19 + 88*x^18 + 91*x^17 + 74*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 42*x^8 + 70*x^7 + 24*x^6 + 30*x^5 + 76*x^4 + 117*x^3 + 56*x^2 + 93*x + 22, x^27 + 33*x^25 + 110*x^24 + 54*x^23 + 40*x^22 + 14*x^21 + 44*x^20 + 51*x^19 + 40*x^18 + 27*x^17 + 98*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 18*x^8 + 102*x^7 + 8*x^6 + 30*x^5 + 108*x^4 + 21*x^3 + 72*x^2 + 29*x + 94, x^27 + 33*x^25 + 42*x^24 + 118*x^23 + 8*x^22 + 46*x^21 + 52*x^20 + 51*x^19 + 40*x^18 + 59*x^17 + 22*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 118*x^8 + 38*x^7 + 104*x^6 + 62*x^5 + 52*x^4 + 21*x^3 + 72*x^2 + 61*x + 10, x^27 + 33*x^25 + 74*x^24 + 22*x^23 + 8*x^22 + 14*x^21 + 52*x^20 + 19*x^19 + 40*x^18 + 91*x^17 + 54*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 86*x^8 + 70*x^7 + 104*x^6 + 30*x^5 + 52*x^4 + 117*x^3 + 72*x^2 + 93*x + 106, x^27 + 33*x^25 + 34*x^24 + 86*x^23 + 24*x^22 + 110*x^21 + 52*x^20 + 19*x^19 + 24*x^18 + 59*x^17 + 78*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 94*x^8 + 6*x^7 + 56*x^6 + 126*x^5 + 116*x^4 + 117*x^3 + 120*x^2 + 61*x + 114, x^27 + 33*x^25 + 50*x^24 + 54*x^23 + 120*x^22 + 78*x^21 + 116*x^20 + 51*x^19 + 56*x^18 + 91*x^17 + 30*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 14*x^8 + 102*x^7 + 24*x^6 + 94*x^5 + 52*x^4 + 21*x^3 + 24*x^2 + 93*x + 98, x^27 + 33*x^25 + 90*x^24 + 6*x^23 + 88*x^22 + 62*x^21 + 100*x^20 + 35*x^19 + 88*x^18 + 43*x^17 + 22*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 38*x^8 + 118*x^7 + 120*x^6 + 14*x^5 + 36*x^4 + 69*x^3 + 56*x^2 + 109*x + 42, x^27 + 33*x^25 + 70*x^24 + 118*x^23 + 88*x^22 + 46*x^21 + 76*x^20 + 51*x^19 + 120*x^18 + 59*x^17 + 90*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 90*x^8 + 38*x^7 + 120*x^6 + 62*x^5 + 76*x^4 + 21*x^3 + 88*x^2 + 61*x + 70, x^27 + 33*x^25 + 50*x^24 + 70*x^23 + 72*x^22 + 94*x^21 + 4*x^20 + 35*x^19 + 104*x^18 + 75*x^17 + 14*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 110*x^8 + 54*x^7 + 40*x^6 + 46*x^5 + 4*x^4 + 69*x^3 + 8*x^2 + 13*x + 18, x^27 + 33*x^25 + 26*x^24 + 22*x^23 + 40*x^22 + 14*x^21 + 52*x^20 + 19*x^19 + 8*x^18 + 91*x^17 + 6*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 70*x^8 + 70*x^7 + 8*x^6 + 30*x^5 + 52*x^4 + 117*x^3 + 40*x^2 + 93*x + 90, x^27 + 33*x^25 + 78*x^24 + 70*x^23 + 120*x^22 + 94*x^21 + 60*x^20 + 35*x^19 + 88*x^18 + 75*x^17 + 50*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 18*x^8 + 54*x^7 + 24*x^6 + 46*x^5 + 60*x^4 + 69*x^3 + 56*x^2 + 13*x + 46, x^27 + 33*x^25 + 34*x^24 + 22*x^23 + 120*x^22 + 110*x^21 + 84*x^20 + 83*x^19 + 56*x^18 + 59*x^17 + 46*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 30*x^8 + 70*x^7 + 24*x^6 + 126*x^5 + 20*x^4 + 53*x^3 + 24*x^2 + 61*x + 82, x^27 + 33*x^25 + 42*x^24 + 22*x^23 + 8*x^22 + 14*x^21 + 116*x^20 + 19*x^19 + 40*x^18 + 91*x^17 + 86*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 118*x^8 + 70*x^7 + 104*x^6 + 30*x^5 + 116*x^4 + 117*x^3 + 72*x^2 + 93*x + 74, x^27 + 33*x^25 + 38*x^24 + 6*x^23 + 72*x^22 + 126*x^21 + 124*x^20 + 35*x^19 + 8*x^18 + 107*x^17 + 10*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 26*x^8 + 118*x^7 + 40*x^6 + 78*x^5 + 60*x^4 + 69*x^3 + 40*x^2 + 45*x + 118, x^27 + 33*x^25 + 58*x^24 + 38*x^23 + 24*x^22 + 30*x^21 + 36*x^20 + 3*x^19 + 24*x^18 + 75*x^17 + 54*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 70*x^8 + 22*x^7 + 56*x^6 + 110*x^5 + 100*x^4 + 37*x^3 + 120*x^2 + 13*x + 10, x^27 + 33*x^25 + 98*x^24 + 102*x^23 + 40*x^22 + 126*x^21 + 4*x^20 + 3*x^19 + 8*x^18 + 43*x^17 + 62*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 126*x^8 + 86*x^7 + 8*x^6 + 78*x^5 + 4*x^4 + 37*x^3 + 40*x^2 + 109*x + 34, x^27 + 33*x^25 + 6*x^24 + 118*x^23 + 120*x^22 + 110*x^21 + 44*x^20 + 51*x^19 + 88*x^18 + 123*x^17 + 58*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 90*x^8 + 38*x^7 + 24*x^6 + 126*x^5 + 44*x^4 + 21*x^3 + 56*x^2 + 125*x + 38, x^27 + 33*x^25 + 10*x^24 + 102*x^23 + 24*x^22 + 30*x^21 + 68*x^20 + 67*x^19 + 24*x^18 + 75*x^17 + 102*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 118*x^8 + 86*x^7 + 56*x^6 + 110*x^5 + 4*x^4 + 101*x^3 + 120*x^2 + 13*x + 90, x^27 + 33*x^25 + 98*x^24 + 22*x^23 + 120*x^22 + 46*x^21 + 20*x^20 + 83*x^19 + 56*x^18 + 123*x^17 + 46*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 94*x^8 + 70*x^7 + 24*x^6 + 62*x^5 + 84*x^4 + 53*x^3 + 24*x^2 + 125*x + 82, x^27 + 33*x^25 + 26*x^24 + 118*x^23 + 40*x^22 + 110*x^21 + 52*x^20 + 51*x^19 + 8*x^18 + 123*x^17 + 6*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 70*x^8 + 38*x^7 + 8*x^6 + 126*x^5 + 52*x^4 + 21*x^3 + 40*x^2 + 125*x + 90, x^27 + 33*x^25 + 22*x^24 + 102*x^23 + 72*x^22 + 94*x^21 + 28*x^20 + 67*x^19 + 8*x^18 + 11*x^17 + 90*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 42*x^8 + 86*x^7 + 40*x^6 + 46*x^5 + 92*x^4 + 101*x^3 + 40*x^2 + 77*x + 38, x^27 + 33*x^25 + 106*x^24 + 102*x^23 + 120*x^22 + 94*x^21 + 36*x^20 + 67*x^19 + 56*x^18 + 11*x^17 + 102*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 86*x^8 + 86*x^7 + 24*x^6 + 46*x^5 + 100*x^4 + 101*x^3 + 24*x^2 + 77*x + 26, x^27 + 33*x^25 + 58*x^24 + 6*x^23 + 88*x^22 + 126*x^21 + 100*x^20 + 35*x^19 + 88*x^18 + 107*x^17 + 118*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 70*x^8 + 118*x^7 + 120*x^6 + 78*x^5 + 36*x^4 + 69*x^3 + 56*x^2 + 45*x + 74, x^27 + 33*x^25 + 86*x^24 + 86*x^23 + 24*x^22 + 14*x^21 + 108*x^20 + 83*x^19 + 56*x^18 + 91*x^17 + 74*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 74*x^8 + 6*x^7 + 56*x^6 + 30*x^5 + 108*x^4 + 53*x^3 + 24*x^2 + 93*x + 86, x^27 + 33*x^25 + 126*x^24 + 86*x^23 + 8*x^22 + 110*x^21 + 44*x^20 + 19*x^19 + 72*x^18 + 59*x^17 + 114*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 66*x^8 + 6*x^7 + 104*x^6 + 126*x^5 + 108*x^4 + 117*x^3 + 104*x^2 + 61*x + 14, x^27 + 33*x^25 + 106*x^24 + 22*x^23 + 104*x^22 + 14*x^21 + 84*x^20 + 19*x^19 + 72*x^18 + 91*x^17 + 54*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 118*x^8 + 70*x^7 + 72*x^6 + 30*x^5 + 84*x^4 + 117*x^3 + 104*x^2 + 93*x + 42, x^27 + 33*x^25 + 10*x^24 + 70*x^23 + 56*x^22 + 126*x^21 + 100*x^20 + 99*x^19 + 120*x^18 + 107*x^17 + 70*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 54*x^8 + 54*x^7 + 88*x^6 + 78*x^5 + 36*x^4 + 5*x^3 + 88*x^2 + 45*x + 58, x^27 + 33*x^25 + 98*x^24 + 70*x^23 + 104*x^22 + 94*x^21 + 68*x^20 + 35*x^19 + 72*x^18 + 75*x^17 + 126*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 126*x^8 + 54*x^7 + 72*x^6 + 46*x^5 + 68*x^4 + 69*x^3 + 104*x^2 + 13*x + 98, x^27 + 33*x^25 + 10*x^24 + 102*x^23 + 88*x^22 + 94*x^21 + 68*x^20 + 67*x^19 + 88*x^18 + 11*x^17 + 102*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 118*x^8 + 86*x^7 + 120*x^6 + 46*x^5 + 4*x^4 + 101*x^3 + 56*x^2 + 77*x + 90, x^27 + 33*x^25 + 86*x^24 + 118*x^23 + 120*x^22 + 110*x^21 + 12*x^20 + 51*x^19 + 88*x^18 + 123*x^17 + 42*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 10*x^8 + 38*x^7 + 24*x^6 + 126*x^5 + 12*x^4 + 21*x^3 + 56*x^2 + 125*x + 54, x^27 + 33*x^25 + 118*x^24 + 70*x^23 + 72*x^22 + 126*x^21 + 28*x^20 + 99*x^19 + 8*x^18 + 107*x^17 + 58*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 74*x^8 + 54*x^7 + 40*x^6 + 78*x^5 + 92*x^4 + 5*x^3 + 40*x^2 + 45*x + 70, x^27 + 33*x^25 + 34*x^24 + 38*x^23 + 72*x^22 + 126*x^21 + 100*x^20 + 67*x^19 + 104*x^18 + 43*x^17 + 30*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 126*x^8 + 22*x^7 + 40*x^6 + 78*x^5 + 100*x^4 + 101*x^3 + 8*x^2 + 109*x + 2, x^27 + 33*x^25 + 6*x^24 + 86*x^23 + 120*x^22 + 78*x^21 + 44*x^20 + 83*x^19 + 88*x^18 + 27*x^17 + 58*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 90*x^8 + 6*x^7 + 24*x^6 + 94*x^5 + 44*x^4 + 53*x^3 + 56*x^2 + 29*x + 38, x^27 + 33*x^25 + 2*x^24 + 54*x^23 + 56*x^22 + 78*x^21 + 20*x^20 + 51*x^19 + 120*x^18 + 91*x^17 + 78*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 62*x^8 + 102*x^7 + 88*x^6 + 94*x^5 + 84*x^4 + 21*x^3 + 88*x^2 + 93*x + 50, x^27 + 33*x^25 + 78*x^24 + 6*x^23 + 88*x^22 + 94*x^21 + 92*x^20 + 99*x^19 + 120*x^18 + 75*x^17 + 18*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 82*x^8 + 118*x^7 + 120*x^6 + 46*x^5 + 92*x^4 + 5*x^3 + 88*x^2 + 13*x + 14, x^27 + 33*x^25 + 118*x^24 + 22*x^23 + 88*x^22 + 14*x^21 + 44*x^20 + 19*x^19 + 120*x^18 + 91*x^17 + 42*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 42*x^8 + 70*x^7 + 120*x^6 + 30*x^5 + 44*x^4 + 117*x^3 + 88*x^2 + 93*x + 118, x^27 + 33*x^25 + 2*x^24 + 70*x^23 + 72*x^22 + 30*x^21 + 36*x^20 + 35*x^19 + 104*x^18 + 11*x^17 + 62*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 30*x^8 + 54*x^7 + 40*x^6 + 110*x^5 + 36*x^4 + 69*x^3 + 8*x^2 + 77*x + 98, x^27 + 33*x^25 + 78*x^24 + 6*x^23 + 24*x^22 + 94*x^21 + 28*x^20 + 99*x^19 + 56*x^18 + 75*x^17 + 82*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 82*x^8 + 118*x^7 + 56*x^6 + 46*x^5 + 28*x^4 + 5*x^3 + 24*x^2 + 13*x + 78, x^27 + 33*x^25 + 50*x^24 + 38*x^23 + 40*x^22 + 62*x^21 + 100*x^20 + 67*x^19 + 8*x^18 + 107*x^17 + 46*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 46*x^8 + 22*x^7 + 8*x^6 + 14*x^5 + 100*x^4 + 101*x^3 + 40*x^2 + 45*x + 50, x^27 + 33*x^25 + 26*x^24 + 118*x^23 + 40*x^22 + 46*x^21 + 116*x^20 + 51*x^19 + 8*x^18 + 59*x^17 + 70*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 70*x^8 + 38*x^7 + 8*x^6 + 62*x^5 + 116*x^4 + 21*x^3 + 40*x^2 + 61*x + 26, x^27 + 33*x^25 + 62*x^24 + 6*x^23 + 120*x^22 + 30*x^21 + 92*x^20 + 99*x^19 + 88*x^18 + 11*x^17 + 2*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 34*x^8 + 118*x^7 + 24*x^6 + 110*x^5 + 92*x^4 + 5*x^3 + 56*x^2 + 77*x + 94, x^27 + 33*x^25 + 82*x^24 + 54*x^23 + 56*x^22 + 78*x^21 + 116*x^20 + 51*x^19 + 120*x^18 + 91*x^17 + 62*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 110*x^8 + 102*x^7 + 88*x^6 + 94*x^5 + 52*x^4 + 21*x^3 + 88*x^2 + 93*x + 66, x^27 + 33*x^25 + 42*x^24 + 22*x^23 + 104*x^22 + 14*x^21 + 84*x^20 + 19*x^19 + 72*x^18 + 91*x^17 + 118*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 54*x^8 + 70*x^7 + 72*x^6 + 30*x^5 + 84*x^4 + 117*x^3 + 104*x^2 + 93*x + 106, x^27 + 33*x^25 + 82*x^24 + 70*x^23 + 104*x^22 + 94*x^21 + 100*x^20 + 35*x^19 + 72*x^18 + 75*x^17 + 78*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 14*x^8 + 54*x^7 + 72*x^6 + 46*x^5 + 100*x^4 + 69*x^3 + 104*x^2 + 13*x + 18, x^27 + 33*x^25 + 70*x^24 + 102*x^23 + 104*x^22 + 94*x^21 + 92*x^20 + 67*x^19 + 104*x^18 + 11*x^17 + 74*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 58*x^8 + 86*x^7 + 72*x^6 + 46*x^5 + 28*x^4 + 101*x^3 + 8*x^2 + 77*x + 118, x^27 + 33*x^25 + 14*x^24 + 6*x^23 + 120*x^22 + 94*x^21 + 124*x^20 + 99*x^19 + 88*x^18 + 75*x^17 + 50*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 82*x^8 + 118*x^7 + 24*x^6 + 46*x^5 + 124*x^4 + 5*x^3 + 56*x^2 + 13*x + 46, x^27 + 33*x^25 + 94*x^24 + 22*x^23 + 40*x^22 + 110*x^21 + 76*x^20 + 83*x^19 + 40*x^18 + 59*x^17 + 50*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 34*x^8 + 70*x^7 + 8*x^6 + 126*x^5 + 12*x^4 + 53*x^3 + 72*x^2 + 61*x + 14, x^27 + 33*x^25 + 50*x^24 + 118*x^23 + 120*x^22 + 14*x^21 + 116*x^20 + 115*x^19 + 56*x^18 + 27*x^17 + 30*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 14*x^8 + 38*x^7 + 24*x^6 + 30*x^5 + 52*x^4 + 85*x^3 + 24*x^2 + 29*x + 98, x^27 + 33*x^25 + 78*x^24 + 102*x^23 + 56*x^22 + 62*x^21 + 60*x^20 + 3*x^19 + 24*x^18 + 107*x^17 + 50*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 18*x^8 + 86*x^7 + 88*x^6 + 14*x^5 + 60*x^4 + 37*x^3 + 120*x^2 + 45*x + 46, x^27 + 33*x^25 + 82*x^24 + 102*x^23 + 40*x^22 + 62*x^21 + 100*x^20 + 3*x^19 + 8*x^18 + 107*x^17 + 78*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 14*x^8 + 86*x^7 + 8*x^6 + 14*x^5 + 100*x^4 + 37*x^3 + 40*x^2 + 45*x + 18, x^27 + 33*x^25 + 34*x^24 + 38*x^23 + 8*x^22 + 62*x^21 + 100*x^20 + 67*x^19 + 40*x^18 + 107*x^17 + 30*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 126*x^8 + 22*x^7 + 104*x^6 + 14*x^5 + 100*x^4 + 101*x^3 + 72*x^2 + 45*x + 2, x^27 + 33*x^25 + 70*x^24 + 70*x^23 + 72*x^22 + 62*x^21 + 60*x^20 + 99*x^19 + 8*x^18 + 43*x^17 + 106*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 122*x^8 + 54*x^7 + 40*x^6 + 14*x^5 + 124*x^4 + 5*x^3 + 40*x^2 + 109*x + 22, x^27 + 33*x^25 + 38*x^24 + 86*x^23 + 24*x^22 + 78*x^21 + 12*x^20 + 83*x^19 + 56*x^18 + 27*x^17 + 122*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 122*x^8 + 6*x^7 + 56*x^6 + 94*x^5 + 12*x^4 + 53*x^3 + 24*x^2 + 29*x + 38, x^27 + 33*x^25 + 58*x^24 + 38*x^23 + 120*x^22 + 30*x^21 + 4*x^20 + 3*x^19 + 56*x^18 + 75*x^17 + 86*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 6*x^8 + 22*x^7 + 24*x^6 + 110*x^5 + 68*x^4 + 37*x^3 + 24*x^2 + 13*x + 42, x^27 + 33*x^25 + 94*x^24 + 38*x^23 + 120*x^22 + 126*x^21 + 92*x^20 + 67*x^19 + 88*x^18 + 43*x^17 + 34*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 2*x^8 + 22*x^7 + 24*x^6 + 78*x^5 + 92*x^4 + 101*x^3 + 56*x^2 + 109*x + 62, x^27 + 33*x^25 + 18*x^24 + 6*x^23 + 72*x^22 + 30*x^21 + 68*x^20 + 99*x^19 + 104*x^18 + 11*x^17 + 46*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 14*x^8 + 118*x^7 + 40*x^6 + 110*x^5 + 68*x^4 + 5*x^3 + 8*x^2 + 77*x + 114, x^27 + 33*x^25 + 42*x^24 + 6*x^23 + 120*x^22 + 126*x^21 + 36*x^20 + 35*x^19 + 56*x^18 + 107*x^17 + 38*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 22*x^8 + 118*x^7 + 24*x^6 + 78*x^5 + 100*x^4 + 69*x^3 + 24*x^2 + 45*x + 90, x^27 + 33*x^25 + 94*x^24 + 102*x^23 + 120*x^22 + 62*x^21 + 92*x^20 + 3*x^19 + 88*x^18 + 107*x^17 + 34*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 2*x^8 + 86*x^7 + 24*x^6 + 14*x^5 + 92*x^4 + 37*x^3 + 56*x^2 + 45*x + 62, x^27 + 33*x^25 + 110*x^24 + 6*x^23 + 24*x^22 + 30*x^21 + 28*x^20 + 99*x^19 + 56*x^18 + 11*x^17 + 114*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 50*x^8 + 118*x^7 + 56*x^6 + 110*x^5 + 28*x^4 + 5*x^3 + 24*x^2 + 77*x + 46, x^27 + 33*x^25 + 122*x^24 + 86*x^23 + 40*x^22 + 14*x^21 + 52*x^20 + 83*x^19 + 8*x^18 + 91*x^17 + 102*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 102*x^8 + 6*x^7 + 8*x^6 + 30*x^5 + 52*x^4 + 53*x^3 + 40*x^2 + 93*x + 122, x^27 + 33*x^25 + 102*x^24 + 6*x^23 + 8*x^22 + 62*x^21 + 124*x^20 + 35*x^19 + 72*x^18 + 43*x^17 + 74*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 90*x^8 + 118*x^7 + 104*x^6 + 14*x^5 + 60*x^4 + 69*x^3 + 104*x^2 + 109*x + 54, x^27 + 33*x^25 + 94*x^24 + 22*x^23 + 104*x^22 + 110*x^21 + 12*x^20 + 83*x^19 + 104*x^18 + 59*x^17 + 114*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 34*x^8 + 70*x^7 + 72*x^6 + 126*x^5 + 76*x^4 + 53*x^3 + 8*x^2 + 61*x + 78, x^27 + 33*x^25 + 54*x^24 + 22*x^23 + 120*x^22 + 78*x^21 + 12*x^20 + 19*x^19 + 88*x^18 + 27*x^17 + 10*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 42*x^8 + 70*x^7 + 24*x^6 + 94*x^5 + 12*x^4 + 117*x^3 + 56*x^2 + 29*x + 86, x^27 + 33*x^25 + 50*x^24 + 70*x^23 + 40*x^22 + 94*x^21 + 100*x^20 + 35*x^19 + 8*x^18 + 75*x^17 + 46*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 46*x^8 + 54*x^7 + 8*x^6 + 46*x^5 + 100*x^4 + 69*x^3 + 40*x^2 + 13*x + 50, x^27 + 33*x^25 + 26*x^24 + 38*x^23 + 88*x^22 + 30*x^21 + 36*x^20 + 3*x^19 + 88*x^18 + 75*x^17 + 22*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 102*x^8 + 22*x^7 + 120*x^6 + 110*x^5 + 100*x^4 + 37*x^3 + 56*x^2 + 13*x + 42, x^27 + 33*x^25 + 66*x^24 + 6*x^23 + 72*x^22 + 94*x^21 + 36*x^20 + 99*x^19 + 104*x^18 + 75*x^17 + 126*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 94*x^8 + 118*x^7 + 40*x^6 + 46*x^5 + 36*x^4 + 5*x^3 + 8*x^2 + 13*x + 34, x^27 + 33*x^25 + 38*x^24 + 102*x^23 + 72*x^22 + 30*x^21 + 60*x^20 + 67*x^19 + 8*x^18 + 75*x^17 + 74*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 26*x^8 + 86*x^7 + 40*x^6 + 110*x^5 + 124*x^4 + 101*x^3 + 40*x^2 + 13*x + 54, x^27 + 33*x^25 + 94*x^24 + 118*x^23 + 40*x^22 + 78*x^21 + 76*x^20 + 115*x^19 + 40*x^18 + 91*x^17 + 50*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 34*x^8 + 38*x^7 + 8*x^6 + 94*x^5 + 12*x^4 + 85*x^3 + 72*x^2 + 93*x + 14, x^27 + 33*x^25 + 26*x^24 + 6*x^23 + 24*x^22 + 126*x^21 + 100*x^20 + 35*x^19 + 24*x^18 + 107*x^17 + 86*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 102*x^8 + 118*x^7 + 56*x^6 + 78*x^5 + 36*x^4 + 69*x^3 + 120*x^2 + 45*x + 106, x^27 + 33*x^25 + 118*x^24 + 86*x^23 + 88*x^22 + 78*x^21 + 44*x^20 + 83*x^19 + 120*x^18 + 27*x^17 + 42*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 42*x^8 + 6*x^7 + 120*x^6 + 94*x^5 + 44*x^4 + 53*x^3 + 88*x^2 + 29*x + 118, x^27 + 33*x^25 + 38*x^24 + 118*x^23 + 56*x^22 + 46*x^21 + 108*x^20 + 51*x^19 + 24*x^18 + 59*x^17 + 26*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 58*x^8 + 38*x^7 + 88*x^6 + 62*x^5 + 108*x^4 + 21*x^3 + 120*x^2 + 61*x + 70, x^27 + 33*x^25 + 2*x^24 + 118*x^23 + 24*x^22 + 78*x^21 + 52*x^20 + 115*x^19 + 24*x^18 + 91*x^17 + 46*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 126*x^8 + 38*x^7 + 56*x^6 + 94*x^5 + 116*x^4 + 85*x^3 + 120*x^2 + 93*x + 18, x^27 + 33*x^25 + 94*x^24 + 118*x^23 + 104*x^22 + 14*x^21 + 76*x^20 + 115*x^19 + 104*x^18 + 27*x^17 + 50*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 34*x^8 + 38*x^7 + 72*x^6 + 30*x^5 + 12*x^4 + 85*x^3 + 8*x^2 + 29*x + 14, x^27 + 33*x^25 + 18*x^24 + 102*x^23 + 40*x^22 + 62*x^21 + 100*x^20 + 3*x^19 + 8*x^18 + 107*x^17 + 14*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 78*x^8 + 86*x^7 + 8*x^6 + 14*x^5 + 100*x^4 + 37*x^3 + 40*x^2 + 45*x + 82, x^27 + 33*x^25 + 114*x^24 + 86*x^23 + 120*x^22 + 110*x^21 + 116*x^20 + 19*x^19 + 56*x^18 + 59*x^17 + 94*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 78*x^8 + 6*x^7 + 24*x^6 + 126*x^5 + 52*x^4 + 117*x^3 + 24*x^2 + 61*x + 34, x^27 + 33*x^25 + 106*x^24 + 118*x^23 + 104*x^22 + 46*x^21 + 20*x^20 + 51*x^19 + 72*x^18 + 59*x^17 + 118*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 118*x^8 + 38*x^7 + 72*x^6 + 62*x^5 + 20*x^4 + 21*x^3 + 104*x^2 + 61*x + 106, x^27 + 33*x^25 + 26*x^24 + 38*x^23 + 24*x^22 + 94*x^21 + 36*x^20 + 3*x^19 + 24*x^18 + 11*x^17 + 22*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 102*x^8 + 22*x^7 + 56*x^6 + 46*x^5 + 100*x^4 + 37*x^3 + 120*x^2 + 77*x + 42, x^27 + 33*x^25 + 122*x^24 + 70*x^23 + 88*x^22 + 126*x^21 + 36*x^20 + 99*x^19 + 88*x^18 + 107*x^17 + 118*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 6*x^8 + 54*x^7 + 120*x^6 + 78*x^5 + 100*x^4 + 5*x^3 + 56*x^2 + 45*x + 74, x^27 + 33*x^25 + 42*x^24 + 54*x^23 + 104*x^22 + 110*x^21 + 20*x^20 + 115*x^19 + 72*x^18 + 123*x^17 + 54*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 54*x^8 + 102*x^7 + 72*x^6 + 126*x^5 + 20*x^4 + 85*x^3 + 104*x^2 + 125*x + 42, x^27 + 33*x^25 + 94*x^24 + 102*x^23 + 24*x^22 + 126*x^21 + 60*x^20 + 3*x^19 + 56*x^18 + 43*x^17 + 66*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 66*x^8 + 86*x^7 + 56*x^6 + 78*x^5 + 60*x^4 + 37*x^3 + 24*x^2 + 109*x + 94, x^27 + 33*x^25 + 30*x^24 + 54*x^23 + 8*x^22 + 78*x^21 + 108*x^20 + 51*x^19 + 72*x^18 + 91*x^17 + 82*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 34*x^8 + 102*x^7 + 104*x^6 + 94*x^5 + 44*x^4 + 21*x^3 + 104*x^2 + 93*x + 46, x^27 + 33*x^25 + 26*x^24 + 6*x^23 + 88*x^22 + 62*x^21 + 100*x^20 + 35*x^19 + 88*x^18 + 43*x^17 + 86*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 102*x^8 + 118*x^7 + 120*x^6 + 14*x^5 + 36*x^4 + 69*x^3 + 56*x^2 + 109*x + 106, x^27 + 33*x^25 + 34*x^24 + 86*x^23 + 120*x^22 + 46*x^21 + 84*x^20 + 19*x^19 + 56*x^18 + 123*x^17 + 46*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 30*x^8 + 6*x^7 + 24*x^6 + 62*x^5 + 20*x^4 + 117*x^3 + 24*x^2 + 125*x + 82, x^27 + 33*x^25 + 2*x^24 + 86*x^23 + 56*x^22 + 110*x^21 + 20*x^20 + 19*x^19 + 120*x^18 + 59*x^17 + 78*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 62*x^8 + 6*x^7 + 88*x^6 + 126*x^5 + 84*x^4 + 117*x^3 + 88*x^2 + 61*x + 50, x^27 + 33*x^25 + 126*x^24 + 102*x^23 + 88*x^22 + 126*x^21 + 60*x^20 + 3*x^19 + 120*x^18 + 43*x^17 + 98*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 34*x^8 + 86*x^7 + 120*x^6 + 78*x^5 + 60*x^4 + 37*x^3 + 88*x^2 + 109*x + 62, x^27 + 33*x^25 + 122*x^24 + 54*x^23 + 40*x^22 + 110*x^21 + 52*x^20 + 115*x^19 + 8*x^18 + 123*x^17 + 102*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 102*x^8 + 102*x^7 + 8*x^6 + 126*x^5 + 52*x^4 + 85*x^3 + 40*x^2 + 125*x + 122, x^27 + 33*x^25 + 30*x^24 + 54*x^23 + 8*x^22 + 14*x^21 + 44*x^20 + 51*x^19 + 72*x^18 + 27*x^17 + 18*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 34*x^8 + 102*x^7 + 104*x^6 + 30*x^5 + 108*x^4 + 21*x^3 + 104*x^2 + 29*x + 110, x^27 + 33*x^25 + 50*x^24 + 6*x^23 + 40*x^22 + 94*x^21 + 36*x^20 + 99*x^19 + 8*x^18 + 75*x^17 + 110*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 46*x^8 + 118*x^7 + 8*x^6 + 46*x^5 + 36*x^4 + 5*x^3 + 40*x^2 + 13*x + 114, x^27 + 33*x^25 + 82*x^24 + 86*x^23 + 56*x^22 + 110*x^21 + 116*x^20 + 19*x^19 + 120*x^18 + 59*x^17 + 62*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 110*x^8 + 6*x^7 + 88*x^6 + 126*x^5 + 52*x^4 + 117*x^3 + 88*x^2 + 61*x + 66, x^27 + 33*x^25 + 82*x^24 + 70*x^23 + 8*x^22 + 94*x^21 + 4*x^20 + 35*x^19 + 40*x^18 + 75*x^17 + 46*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 78*x^8 + 54*x^7 + 104*x^6 + 46*x^5 + 4*x^4 + 69*x^3 + 72*x^2 + 13*x + 114, x^27 + 33*x^25 + 26*x^24 + 54*x^23 + 104*x^22 + 110*x^21 + 52*x^20 + 115*x^19 + 72*x^18 + 123*x^17 + 6*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 70*x^8 + 102*x^7 + 72*x^6 + 126*x^5 + 52*x^4 + 85*x^3 + 104*x^2 + 125*x + 90, x^27 + 33*x^25 + 74*x^24 + 102*x^23 + 24*x^22 + 94*x^21 + 4*x^20 + 67*x^19 + 24*x^18 + 11*x^17 + 102*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 54*x^8 + 86*x^7 + 56*x^6 + 46*x^5 + 68*x^4 + 101*x^3 + 120*x^2 + 77*x + 90, x^27 + 33*x^25 + 102*x^24 + 22*x^23 + 88*x^22 + 78*x^21 + 12*x^20 + 19*x^19 + 120*x^18 + 27*x^17 + 58*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 58*x^8 + 70*x^7 + 120*x^6 + 94*x^5 + 12*x^4 + 117*x^3 + 88*x^2 + 29*x + 102, x^27 + 33*x^25 + 54*x^24 + 54*x^23 + 120*x^22 + 110*x^21 + 12*x^20 + 115*x^19 + 88*x^18 + 123*x^17 + 10*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 42*x^8 + 102*x^7 + 24*x^6 + 126*x^5 + 12*x^4 + 85*x^3 + 56*x^2 + 125*x + 86, x^27 + 33*x^25 + 102*x^24 + 86*x^23 + 88*x^22 + 14*x^21 + 12*x^20 + 83*x^19 + 120*x^18 + 91*x^17 + 58*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 58*x^8 + 6*x^7 + 120*x^6 + 30*x^5 + 12*x^4 + 53*x^3 + 88*x^2 + 93*x + 102, x^27 + 33*x^25 + 82*x^24 + 22*x^23 + 24*x^22 + 110*x^21 + 20*x^20 + 83*x^19 + 24*x^18 + 59*x^17 + 30*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 46*x^8 + 70*x^7 + 56*x^6 + 126*x^5 + 84*x^4 + 53*x^3 + 120*x^2 + 61*x + 34, x^27 + 33*x^25 + 26*x^24 + 118*x^23 + 8*x^22 + 110*x^21 + 20*x^20 + 51*x^19 + 40*x^18 + 123*x^17 + 38*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 6*x^8 + 38*x^7 + 104*x^6 + 126*x^5 + 20*x^4 + 21*x^3 + 72*x^2 + 125*x + 122, x^27 + 33*x^25 + 110*x^24 + 102*x^23 + 88*x^22 + 126*x^21 + 92*x^20 + 3*x^19 + 120*x^18 + 43*x^17 + 50*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 50*x^8 + 86*x^7 + 120*x^6 + 78*x^5 + 92*x^4 + 37*x^3 + 88*x^2 + 109*x + 110, x^27 + 33*x^25 + 18*x^24 + 22*x^23 + 56*x^22 + 110*x^21 + 52*x^20 + 83*x^19 + 120*x^18 + 59*x^17 + 62*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 46*x^8 + 70*x^7 + 88*x^6 + 126*x^5 + 116*x^4 + 53*x^3 + 88*x^2 + 61*x + 66, x^27 + 33*x^25 + 42*x^24 + 70*x^23 + 56*x^22 + 62*x^21 + 100*x^20 + 99*x^19 + 120*x^18 + 43*x^17 + 102*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 22*x^8 + 54*x^7 + 88*x^6 + 14*x^5 + 36*x^4 + 5*x^3 + 88*x^2 + 109*x + 26, x^27 + 33*x^25 + 106*x^24 + 6*x^23 + 88*x^22 + 126*x^21 + 4*x^20 + 35*x^19 + 88*x^18 + 107*x^17 + 6*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 22*x^8 + 118*x^7 + 120*x^6 + 78*x^5 + 68*x^4 + 69*x^3 + 56*x^2 + 45*x + 58, x^27 + 33*x^25 + 122*x^24 + 22*x^23 + 8*x^22 + 14*x^21 + 84*x^20 + 19*x^19 + 40*x^18 + 91*x^17 + 70*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 38*x^8 + 70*x^7 + 104*x^6 + 30*x^5 + 84*x^4 + 117*x^3 + 72*x^2 + 93*x + 90, x^27 + 33*x^25 + 114*x^24 + 86*x^23 + 120*x^22 + 46*x^21 + 52*x^20 + 19*x^19 + 56*x^18 + 123*x^17 + 30*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 78*x^8 + 6*x^7 + 24*x^6 + 62*x^5 + 116*x^4 + 117*x^3 + 24*x^2 + 125*x + 98, x^27 + 33*x^25 + 118*x^24 + 118*x^23 + 120*x^22 + 46*x^21 + 12*x^20 + 51*x^19 + 88*x^18 + 59*x^17 + 74*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 106*x^8 + 38*x^7 + 24*x^6 + 62*x^5 + 12*x^4 + 21*x^3 + 56*x^2 + 61*x + 22, x^27 + 33*x^25 + 2*x^24 + 70*x^23 + 40*x^22 + 30*x^21 + 4*x^20 + 35*x^19 + 8*x^18 + 11*x^17 + 94*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 94*x^8 + 54*x^7 + 8*x^6 + 110*x^5 + 4*x^4 + 69*x^3 + 40*x^2 + 77*x + 2, x^27 + 33*x^25 + 122*x^24 + 102*x^23 + 120*x^22 + 30*x^21 + 68*x^20 + 67*x^19 + 56*x^18 + 75*x^17 + 86*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 70*x^8 + 86*x^7 + 24*x^6 + 110*x^5 + 4*x^4 + 101*x^3 + 24*x^2 + 13*x + 42, x^27 + 33*x^25 + 62*x^24 + 86*x^23 + 72*x^22 + 110*x^21 + 108*x^20 + 19*x^19 + 8*x^18 + 59*x^17 + 114*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 2*x^8 + 6*x^7 + 40*x^6 + 126*x^5 + 44*x^4 + 117*x^3 + 40*x^2 + 61*x + 14, x^27 + 33*x^25 + 10*x^24 + 6*x^23 + 88*x^22 + 62*x^21 + 4*x^20 + 35*x^19 + 88*x^18 + 43*x^17 + 38*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 118*x^8 + 118*x^7 + 120*x^6 + 14*x^5 + 68*x^4 + 69*x^3 + 56*x^2 + 109*x + 26, x^27 + 33*x^25 + 18*x^24 + 118*x^23 + 120*x^22 + 14*x^21 + 52*x^20 + 115*x^19 + 56*x^18 + 27*x^17 + 62*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 46*x^8 + 38*x^7 + 24*x^6 + 30*x^5 + 116*x^4 + 85*x^3 + 24*x^2 + 29*x + 66, x^27 + 33*x^25 + 86*x^24 + 102*x^23 + 72*x^22 + 94*x^21 + 28*x^20 + 67*x^19 + 8*x^18 + 11*x^17 + 26*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 106*x^8 + 86*x^7 + 40*x^6 + 46*x^5 + 92*x^4 + 101*x^3 + 40*x^2 + 77*x + 102, x^27 + 33*x^25 + 18*x^24 + 54*x^23 + 88*x^22 + 14*x^21 + 84*x^20 + 51*x^19 + 88*x^18 + 27*x^17 + 30*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 110*x^8 + 102*x^7 + 120*x^6 + 30*x^5 + 20*x^4 + 21*x^3 + 56*x^2 + 29*x + 34, x^27 + 33*x^25 + 70*x^24 + 22*x^23 + 56*x^22 + 14*x^21 + 108*x^20 + 19*x^19 + 24*x^18 + 91*x^17 + 58*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 26*x^8 + 70*x^7 + 88*x^6 + 30*x^5 + 108*x^4 + 117*x^3 + 120*x^2 + 93*x + 38, x^27 + 33*x^25 + 110*x^24 + 54*x^23 + 8*x^22 + 78*x^21 + 76*x^20 + 51*x^19 + 72*x^18 + 91*x^17 + 66*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 82*x^8 + 102*x^7 + 104*x^6 + 94*x^5 + 12*x^4 + 21*x^3 + 104*x^2 + 93*x + 62, x^27 + 33*x^25 + 82*x^24 + 54*x^23 + 120*x^22 + 14*x^21 + 116*x^20 + 51*x^19 + 56*x^18 + 27*x^17 + 62*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 110*x^8 + 102*x^7 + 24*x^6 + 30*x^5 + 52*x^4 + 21*x^3 + 24*x^2 + 29*x + 66, x^27 + 33*x^25 + 30*x^24 + 38*x^23 + 88*x^22 + 126*x^21 + 60*x^20 + 67*x^19 + 120*x^18 + 43*x^17 + 2*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 2*x^8 + 22*x^7 + 120*x^6 + 78*x^5 + 60*x^4 + 101*x^3 + 88*x^2 + 109*x + 30, x^27 + 33*x^25 + 122*x^24 + 118*x^23 + 8*x^22 + 110*x^21 + 84*x^20 + 51*x^19 + 40*x^18 + 123*x^17 + 70*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 38*x^8 + 38*x^7 + 104*x^6 + 126*x^5 + 84*x^4 + 21*x^3 + 72*x^2 + 125*x + 90, x^27 + 33*x^25 + 30*x^24 + 118*x^23 + 40*x^22 + 78*x^21 + 76*x^20 + 115*x^19 + 40*x^18 + 91*x^17 + 114*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 98*x^8 + 38*x^7 + 8*x^6 + 94*x^5 + 12*x^4 + 85*x^3 + 72*x^2 + 93*x + 78, x^27 + 33*x^25 + 94*x^24 + 86*x^23 + 40*x^22 + 46*x^21 + 76*x^20 + 19*x^19 + 40*x^18 + 123*x^17 + 50*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 34*x^8 + 6*x^7 + 8*x^6 + 62*x^5 + 12*x^4 + 117*x^3 + 72*x^2 + 125*x + 14, x^27 + 33*x^25 + 54*x^24 + 86*x^23 + 24*x^22 + 78*x^21 + 108*x^20 + 83*x^19 + 56*x^18 + 27*x^17 + 42*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 106*x^8 + 6*x^7 + 56*x^6 + 94*x^5 + 108*x^4 + 53*x^3 + 24*x^2 + 29*x + 118, x^27 + 33*x^25 + 10*x^24 + 22*x^23 + 8*x^22 + 78*x^21 + 116*x^20 + 19*x^19 + 40*x^18 + 27*x^17 + 54*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 22*x^8 + 70*x^7 + 104*x^6 + 94*x^5 + 116*x^4 + 117*x^3 + 72*x^2 + 29*x + 106, x^27 + 33*x^25 + 2*x^24 + 86*x^23 + 24*x^22 + 46*x^21 + 52*x^20 + 19*x^19 + 24*x^18 + 123*x^17 + 46*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 126*x^8 + 6*x^7 + 56*x^6 + 62*x^5 + 116*x^4 + 117*x^3 + 120*x^2 + 125*x + 18, x^27 + 33*x^25 + 82*x^24 + 54*x^23 + 24*x^22 + 78*x^21 + 84*x^20 + 51*x^19 + 24*x^18 + 91*x^17 + 94*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 46*x^8 + 102*x^7 + 56*x^6 + 94*x^5 + 20*x^4 + 21*x^3 + 120*x^2 + 93*x + 98, x^27 + 33*x^25 + 90*x^24 + 38*x^23 + 24*x^22 + 30*x^21 + 100*x^20 + 3*x^19 + 24*x^18 + 75*x^17 + 22*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 38*x^8 + 22*x^7 + 56*x^6 + 110*x^5 + 36*x^4 + 37*x^3 + 120*x^2 + 13*x + 42, x^27 + 33*x^25 + 18*x^24 + 102*x^23 + 104*x^22 + 126*x^21 + 100*x^20 + 3*x^19 + 72*x^18 + 43*x^17 + 14*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 78*x^8 + 86*x^7 + 72*x^6 + 78*x^5 + 100*x^4 + 37*x^3 + 104*x^2 + 109*x + 82, x^27 + 33*x^25 + 26*x^24 + 6*x^23 + 120*x^22 + 62*x^21 + 4*x^20 + 35*x^19 + 56*x^18 + 43*x^17 + 54*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 38*x^8 + 118*x^7 + 24*x^6 + 14*x^5 + 68*x^4 + 69*x^3 + 24*x^2 + 109*x + 74, x^27 + 33*x^25 + 86*x^24 + 6*x^23 + 72*x^22 + 62*x^21 + 92*x^20 + 35*x^19 + 8*x^18 + 43*x^17 + 90*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 106*x^8 + 118*x^7 + 40*x^6 + 14*x^5 + 28*x^4 + 69*x^3 + 40*x^2 + 109*x + 38, x^27 + 33*x^25 + 18*x^24 + 38*x^23 + 40*x^22 + 62*x^21 + 36*x^20 + 67*x^19 + 8*x^18 + 107*x^17 + 78*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 78*x^8 + 22*x^7 + 8*x^6 + 14*x^5 + 36*x^4 + 101*x^3 + 40*x^2 + 45*x + 18, x^27 + 33*x^25 + 26*x^24 + 22*x^23 + 104*x^22 + 14*x^21 + 116*x^20 + 19*x^19 + 72*x^18 + 91*x^17 + 70*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 70*x^8 + 70*x^7 + 72*x^6 + 30*x^5 + 116*x^4 + 117*x^3 + 104*x^2 + 93*x + 26, x^27 + 33*x^25 + 2*x^24 + 38*x^23 + 8*x^22 + 126*x^21 + 100*x^20 + 67*x^19 + 40*x^18 + 43*x^17 + 126*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 30*x^8 + 22*x^7 + 104*x^6 + 78*x^5 + 100*x^4 + 101*x^3 + 72*x^2 + 109*x + 34, x^27 + 33*x^25 + 122*x^24 + 86*x^23 + 8*x^22 + 78*x^21 + 84*x^20 + 83*x^19 + 40*x^18 + 27*x^17 + 70*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 38*x^8 + 6*x^7 + 104*x^6 + 94*x^5 + 84*x^4 + 53*x^3 + 72*x^2 + 29*x + 90, x^27 + 33*x^25 + 78*x^24 + 38*x^23 + 88*x^22 + 126*x^21 + 92*x^20 + 67*x^19 + 120*x^18 + 43*x^17 + 18*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 82*x^8 + 22*x^7 + 120*x^6 + 78*x^5 + 92*x^4 + 101*x^3 + 88*x^2 + 109*x + 14, x^27 + 33*x^25 + 58*x^24 + 22*x^23 + 40*x^22 + 78*x^21 + 52*x^20 + 19*x^19 + 8*x^18 + 27*x^17 + 38*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 38*x^8 + 70*x^7 + 8*x^6 + 94*x^5 + 52*x^4 + 117*x^3 + 40*x^2 + 29*x + 58, x^27 + 33*x^25 + 78*x^24 + 38*x^23 + 24*x^22 + 126*x^21 + 28*x^20 + 67*x^19 + 56*x^18 + 43*x^17 + 82*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 82*x^8 + 22*x^7 + 56*x^6 + 78*x^5 + 28*x^4 + 101*x^3 + 24*x^2 + 109*x + 78, x^27 + 33*x^25 + 38*x^24 + 118*x^23 + 24*x^22 + 110*x^21 + 12*x^20 + 51*x^19 + 56*x^18 + 123*x^17 + 122*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 122*x^8 + 38*x^7 + 56*x^6 + 126*x^5 + 12*x^4 + 21*x^3 + 24*x^2 + 125*x + 38, x^27 + 33*x^25 + 74*x^24 + 102*x^23 + 88*x^22 + 30*x^21 + 4*x^20 + 67*x^19 + 88*x^18 + 75*x^17 + 102*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 54*x^8 + 86*x^7 + 120*x^6 + 110*x^5 + 68*x^4 + 101*x^3 + 56*x^2 + 13*x + 90, x^27 + 33*x^25 + 86*x^24 + 22*x^23 + 24*x^22 + 14*x^21 + 44*x^20 + 19*x^19 + 56*x^18 + 91*x^17 + 10*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 74*x^8 + 70*x^7 + 56*x^6 + 30*x^5 + 44*x^4 + 117*x^3 + 24*x^2 + 93*x + 22, x^27 + 33*x^25 + 78*x^24 + 102*x^23 + 88*x^22 + 62*x^21 + 92*x^20 + 3*x^19 + 120*x^18 + 107*x^17 + 18*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 82*x^8 + 86*x^7 + 120*x^6 + 14*x^5 + 92*x^4 + 37*x^3 + 88*x^2 + 45*x + 14, x^27 + 33*x^25 + 70*x^24 + 70*x^23 + 8*x^22 + 62*x^21 + 124*x^20 + 99*x^19 + 72*x^18 + 43*x^17 + 42*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 122*x^8 + 54*x^7 + 104*x^6 + 14*x^5 + 60*x^4 + 5*x^3 + 104*x^2 + 109*x + 86, x^27 + 33*x^25 + 90*x^24 + 6*x^23 + 24*x^22 + 62*x^21 + 36*x^20 + 35*x^19 + 24*x^18 + 43*x^17 + 86*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 38*x^8 + 118*x^7 + 56*x^6 + 14*x^5 + 100*x^4 + 69*x^3 + 120*x^2 + 109*x + 106, x^27 + 33*x^25 + 22*x^24 + 54*x^23 + 24*x^22 + 110*x^21 + 108*x^20 + 115*x^19 + 56*x^18 + 123*x^17 + 10*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 10*x^8 + 102*x^7 + 56*x^6 + 126*x^5 + 108*x^4 + 85*x^3 + 24*x^2 + 125*x + 22, x^27 + 33*x^25 + 70*x^24 + 6*x^23 + 72*x^22 + 126*x^21 + 60*x^20 + 35*x^19 + 8*x^18 + 107*x^17 + 106*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 122*x^8 + 118*x^7 + 40*x^6 + 78*x^5 + 124*x^4 + 69*x^3 + 40*x^2 + 45*x + 22, x^27 + 33*x^25 + 74*x^24 + 22*x^23 + 72*x^22 + 14*x^21 + 116*x^20 + 19*x^19 + 104*x^18 + 91*x^17 + 118*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 86*x^8 + 70*x^7 + 40*x^6 + 30*x^5 + 116*x^4 + 117*x^3 + 8*x^2 + 93*x + 42, x^27 + 33*x^25 + 102*x^24 + 54*x^23 + 24*x^22 + 46*x^21 + 12*x^20 + 115*x^19 + 56*x^18 + 59*x^17 + 58*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 58*x^8 + 102*x^7 + 56*x^6 + 62*x^5 + 12*x^4 + 85*x^3 + 24*x^2 + 61*x + 102, x^27 + 33*x^25 + 118*x^24 + 102*x^23 + 72*x^22 + 30*x^21 + 28*x^20 + 67*x^19 + 8*x^18 + 75*x^17 + 58*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 74*x^8 + 86*x^7 + 40*x^6 + 110*x^5 + 92*x^4 + 101*x^3 + 40*x^2 + 13*x + 70, x^27 + 33*x^25 + 14*x^24 + 70*x^23 + 120*x^22 + 94*x^21 + 60*x^20 + 35*x^19 + 88*x^18 + 75*x^17 + 114*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 82*x^8 + 54*x^7 + 24*x^6 + 46*x^5 + 60*x^4 + 69*x^3 + 56*x^2 + 13*x + 110, x^27 + 33*x^25 + 34*x^24 + 102*x^23 + 72*x^22 + 62*x^21 + 100*x^20 + 3*x^19 + 104*x^18 + 107*x^17 + 30*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 126*x^8 + 86*x^7 + 40*x^6 + 14*x^5 + 100*x^4 + 37*x^3 + 8*x^2 + 45*x + 2, x^27 + 33*x^25 + 2*x^24 + 54*x^23 + 88*x^22 + 78*x^21 + 52*x^20 + 51*x^19 + 88*x^18 + 91*x^17 + 46*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 126*x^8 + 102*x^7 + 120*x^6 + 94*x^5 + 116*x^4 + 21*x^3 + 56*x^2 + 93*x + 18, x^27 + 33*x^25 + 106*x^24 + 70*x^23 + 24*x^22 + 62*x^21 + 68*x^20 + 99*x^19 + 24*x^18 + 43*x^17 + 70*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 22*x^8 + 54*x^7 + 56*x^6 + 14*x^5 + 4*x^4 + 5*x^3 + 120*x^2 + 109*x + 122, x^27 + 33*x^25 + 74*x^24 + 86*x^23 + 40*x^22 + 14*x^21 + 20*x^20 + 83*x^19 + 8*x^18 + 91*x^17 + 86*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 22*x^8 + 6*x^7 + 8*x^6 + 30*x^5 + 20*x^4 + 53*x^3 + 40*x^2 + 93*x + 10, x^27 + 33*x^25 + 2*x^24 + 54*x^23 + 120*x^22 + 14*x^21 + 20*x^20 + 51*x^19 + 56*x^18 + 27*x^17 + 78*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 62*x^8 + 102*x^7 + 24*x^6 + 30*x^5 + 84*x^4 + 21*x^3 + 24*x^2 + 29*x + 50, x^27 + 33*x^25 + 74*x^24 + 22*x^23 + 104*x^22 + 78*x^21 + 84*x^20 + 19*x^19 + 72*x^18 + 27*x^17 + 22*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 22*x^8 + 70*x^7 + 72*x^6 + 94*x^5 + 84*x^4 + 117*x^3 + 104*x^2 + 29*x + 74, x^27 + 33*x^25 + 46*x^24 + 22*x^23 + 104*x^22 + 110*x^21 + 108*x^20 + 83*x^19 + 104*x^18 + 59*x^17 + 98*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 82*x^8 + 70*x^7 + 72*x^6 + 126*x^5 + 44*x^4 + 53*x^3 + 8*x^2 + 61*x + 94, x^27 + 33*x^25 + 98*x^24 + 118*x^23 + 56*x^22 + 78*x^21 + 20*x^20 + 115*x^19 + 120*x^18 + 91*x^17 + 46*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 94*x^8 + 38*x^7 + 88*x^6 + 94*x^5 + 84*x^4 + 85*x^3 + 88*x^2 + 93*x + 82, x^27 + 33*x^25 + 58*x^24 + 86*x^23 + 72*x^22 + 14*x^21 + 84*x^20 + 83*x^19 + 104*x^18 + 91*x^17 + 6*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 102*x^8 + 6*x^7 + 40*x^6 + 30*x^5 + 84*x^4 + 53*x^3 + 8*x^2 + 93*x + 26, x^27 + 33*x^25 + 2*x^24 + 118*x^23 + 88*x^22 + 78*x^21 + 116*x^20 + 115*x^19 + 88*x^18 + 91*x^17 + 110*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 126*x^8 + 38*x^7 + 120*x^6 + 94*x^5 + 52*x^4 + 85*x^3 + 56*x^2 + 93*x + 82, x^27 + 33*x^25 + 90*x^24 + 102*x^23 + 56*x^22 + 30*x^21 + 68*x^20 + 67*x^19 + 120*x^18 + 75*x^17 + 54*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 102*x^8 + 86*x^7 + 88*x^6 + 110*x^5 + 4*x^4 + 101*x^3 + 88*x^2 + 13*x + 74, x^27 + 33*x^25 + 62*x^24 + 118*x^23 + 40*x^22 + 14*x^21 + 76*x^20 + 115*x^19 + 40*x^18 + 27*x^17 + 18*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 66*x^8 + 38*x^7 + 8*x^6 + 30*x^5 + 12*x^4 + 85*x^3 + 72*x^2 + 29*x + 46, x^27 + 33*x^25 + 26*x^24 + 70*x^23 + 24*x^22 + 126*x^21 + 36*x^20 + 99*x^19 + 24*x^18 + 107*x^17 + 22*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 102*x^8 + 54*x^7 + 56*x^6 + 78*x^5 + 100*x^4 + 5*x^3 + 120*x^2 + 45*x + 42, x^27 + 33*x^25 + 114*x^24 + 38*x^23 + 8*x^22 + 62*x^21 + 68*x^20 + 67*x^19 + 40*x^18 + 107*x^17 + 14*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 46*x^8 + 22*x^7 + 104*x^6 + 14*x^5 + 68*x^4 + 101*x^3 + 72*x^2 + 45*x + 18, x^27 + 33*x^25 + 2*x^24 + 54*x^23 + 120*x^22 + 78*x^21 + 84*x^20 + 51*x^19 + 56*x^18 + 91*x^17 + 14*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 62*x^8 + 102*x^7 + 24*x^6 + 94*x^5 + 20*x^4 + 21*x^3 + 24*x^2 + 93*x + 114, x^27 + 33*x^25 + 66*x^24 + 38*x^23 + 72*x^22 + 126*x^21 + 36*x^20 + 67*x^19 + 104*x^18 + 43*x^17 + 126*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 94*x^8 + 22*x^7 + 40*x^6 + 78*x^5 + 36*x^4 + 101*x^3 + 8*x^2 + 109*x + 34, x^27 + 33*x^25 + 70*x^24 + 54*x^23 + 120*x^22 + 110*x^21 + 108*x^20 + 115*x^19 + 88*x^18 + 123*x^17 + 58*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 26*x^8 + 102*x^7 + 24*x^6 + 126*x^5 + 108*x^4 + 85*x^3 + 56*x^2 + 125*x + 38, x^27 + 33*x^25 + 50*x^24 + 102*x^23 + 104*x^22 + 126*x^21 + 36*x^20 + 3*x^19 + 72*x^18 + 43*x^17 + 110*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 46*x^8 + 86*x^7 + 72*x^6 + 78*x^5 + 36*x^4 + 37*x^3 + 104*x^2 + 109*x + 114, x^27 + 33*x^25 + 66*x^24 + 102*x^23 + 72*x^22 + 62*x^21 + 36*x^20 + 3*x^19 + 104*x^18 + 107*x^17 + 126*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 94*x^8 + 86*x^7 + 40*x^6 + 14*x^5 + 36*x^4 + 37*x^3 + 8*x^2 + 45*x + 34, x^27 + 33*x^25 + 38*x^24 + 70*x^23 + 8*x^22 + 62*x^21 + 60*x^20 + 99*x^19 + 72*x^18 + 43*x^17 + 74*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 26*x^8 + 54*x^7 + 104*x^6 + 14*x^5 + 124*x^4 + 5*x^3 + 104*x^2 + 109*x + 54, x^27 + 33*x^25 + 82*x^24 + 70*x^23 + 72*x^22 + 94*x^21 + 68*x^20 + 35*x^19 + 104*x^18 + 75*x^17 + 110*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 78*x^8 + 54*x^7 + 40*x^6 + 46*x^5 + 68*x^4 + 69*x^3 + 8*x^2 + 13*x + 50, x^27 + 33*x^25 + 62*x^24 + 38*x^23 + 88*x^22 + 126*x^21 + 124*x^20 + 67*x^19 + 120*x^18 + 43*x^17 + 98*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 98*x^8 + 22*x^7 + 120*x^6 + 78*x^5 + 124*x^4 + 101*x^3 + 88*x^2 + 109*x + 62, x^27 + 33*x^25 + 54*x^24 + 54*x^23 + 56*x^22 + 110*x^21 + 76*x^20 + 115*x^19 + 24*x^18 + 123*x^17 + 74*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 42*x^8 + 102*x^7 + 88*x^6 + 126*x^5 + 76*x^4 + 85*x^3 + 120*x^2 + 125*x + 22, x^27 + 33*x^25 + 58*x^24 + 54*x^23 + 72*x^22 + 110*x^21 + 84*x^20 + 115*x^19 + 104*x^18 + 123*x^17 + 6*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 102*x^8 + 102*x^7 + 40*x^6 + 126*x^5 + 84*x^4 + 85*x^3 + 8*x^2 + 125*x + 26, x^27 + 33*x^25 + 94*x^24 + 38*x^23 + 120*x^22 + 62*x^21 + 28*x^20 + 67*x^19 + 88*x^18 + 107*x^17 + 98*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 2*x^8 + 22*x^7 + 24*x^6 + 14*x^5 + 28*x^4 + 101*x^3 + 56*x^2 + 45*x + 126, x^27 + 33*x^25 + 118*x^24 + 118*x^23 + 56*x^22 + 46*x^21 + 76*x^20 + 51*x^19 + 24*x^18 + 59*x^17 + 10*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 106*x^8 + 38*x^7 + 88*x^6 + 62*x^5 + 76*x^4 + 21*x^3 + 120*x^2 + 61*x + 86, x^27 + 33*x^25 + 70*x^24 + 22*x^23 + 88*x^22 + 14*x^21 + 12*x^20 + 19*x^19 + 120*x^18 + 91*x^17 + 26*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 90*x^8 + 70*x^7 + 120*x^6 + 30*x^5 + 12*x^4 + 117*x^3 + 88*x^2 + 93*x + 6, x^27 + 33*x^25 + 126*x^24 + 38*x^23 + 120*x^22 + 62*x^21 + 92*x^20 + 67*x^19 + 88*x^18 + 107*x^17 + 66*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 98*x^8 + 22*x^7 + 24*x^6 + 14*x^5 + 92*x^4 + 101*x^3 + 56*x^2 + 45*x + 30, x^27 + 33*x^25 + 82*x^24 + 22*x^23 + 56*x^22 + 110*x^21 + 52*x^20 + 83*x^19 + 120*x^18 + 59*x^17 + 126*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 110*x^8 + 70*x^7 + 88*x^6 + 126*x^5 + 116*x^4 + 53*x^3 + 88*x^2 + 61*x + 2, x^27 + 33*x^25 + 58*x^24 + 22*x^23 + 104*x^22 + 78*x^21 + 116*x^20 + 19*x^19 + 72*x^18 + 27*x^17 + 102*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 38*x^8 + 70*x^7 + 72*x^6 + 94*x^5 + 116*x^4 + 117*x^3 + 104*x^2 + 29*x + 122, x^27 + 33*x^25 + 2*x^24 + 6*x^23 + 72*x^22 + 30*x^21 + 100*x^20 + 99*x^19 + 104*x^18 + 11*x^17 + 126*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 30*x^8 + 118*x^7 + 40*x^6 + 110*x^5 + 100*x^4 + 5*x^3 + 8*x^2 + 77*x + 34, x^27 + 33*x^25 + 106*x^24 + 86*x^23 + 40*x^22 + 14*x^21 + 84*x^20 + 83*x^19 + 8*x^18 + 91*x^17 + 54*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 118*x^8 + 6*x^7 + 8*x^6 + 30*x^5 + 84*x^4 + 53*x^3 + 40*x^2 + 93*x + 42, x^27 + 33*x^25 + 82*x^24 + 86*x^23 + 56*x^22 + 46*x^21 + 52*x^20 + 19*x^19 + 120*x^18 + 123*x^17 + 126*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 110*x^8 + 6*x^7 + 88*x^6 + 62*x^5 + 116*x^4 + 117*x^3 + 88*x^2 + 125*x + 2, x^27 + 33*x^25 + 102*x^24 + 54*x^23 + 120*x^22 + 46*x^21 + 108*x^20 + 115*x^19 + 88*x^18 + 59*x^17 + 90*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 122*x^8 + 102*x^7 + 24*x^6 + 62*x^5 + 108*x^4 + 85*x^3 + 56*x^2 + 61*x + 6, x^27 + 33*x^25 + 86*x^24 + 102*x^23 + 40*x^22 + 30*x^21 + 60*x^20 + 67*x^19 + 40*x^18 + 75*x^17 + 122*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 42*x^8 + 86*x^7 + 8*x^6 + 110*x^5 + 124*x^4 + 101*x^3 + 72*x^2 + 13*x + 70, x^27 + 33*x^25 + 102*x^24 + 118*x^23 + 120*x^22 + 46*x^21 + 44*x^20 + 51*x^19 + 88*x^18 + 59*x^17 + 26*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 122*x^8 + 38*x^7 + 24*x^6 + 62*x^5 + 44*x^4 + 21*x^3 + 56*x^2 + 61*x + 70, x^27 + 33*x^25 + 62*x^24 + 70*x^23 + 56*x^22 + 94*x^21 + 28*x^20 + 35*x^19 + 24*x^18 + 75*x^17 + 66*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 34*x^8 + 54*x^7 + 88*x^6 + 46*x^5 + 28*x^4 + 69*x^3 + 120*x^2 + 13*x + 30, x^27 + 33*x^25 + 46*x^24 + 54*x^23 + 8*x^22 + 78*x^21 + 76*x^20 + 51*x^19 + 72*x^18 + 91*x^17 + 2*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 18*x^8 + 102*x^7 + 104*x^6 + 94*x^5 + 12*x^4 + 21*x^3 + 104*x^2 + 93*x + 126, x^27 + 33*x^25 + 74*x^24 + 102*x^23 + 56*x^22 + 30*x^21 + 100*x^20 + 67*x^19 + 120*x^18 + 75*x^17 + 6*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 118*x^8 + 86*x^7 + 88*x^6 + 110*x^5 + 36*x^4 + 101*x^3 + 88*x^2 + 13*x + 122, x^27 + 33*x^25 + 46*x^24 + 118*x^23 + 72*x^22 + 78*x^21 + 76*x^20 + 115*x^19 + 8*x^18 + 91*x^17 + 2*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 18*x^8 + 38*x^7 + 40*x^6 + 94*x^5 + 12*x^4 + 85*x^3 + 40*x^2 + 93*x + 126, x^27 + 33*x^25 + 58*x^24 + 38*x^23 + 56*x^22 + 30*x^21 + 68*x^20 + 3*x^19 + 120*x^18 + 75*x^17 + 22*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 6*x^8 + 22*x^7 + 88*x^6 + 110*x^5 + 4*x^4 + 37*x^3 + 88*x^2 + 13*x + 106, x^27 + 33*x^25 + 70*x^24 + 86*x^23 + 56*x^22 + 78*x^21 + 108*x^20 + 83*x^19 + 24*x^18 + 27*x^17 + 58*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 26*x^8 + 6*x^7 + 88*x^6 + 94*x^5 + 108*x^4 + 53*x^3 + 120*x^2 + 29*x + 38, x^27 + 33*x^25 + 34*x^24 + 86*x^23 + 56*x^22 + 110*x^21 + 84*x^20 + 19*x^19 + 120*x^18 + 59*x^17 + 46*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 30*x^8 + 6*x^7 + 88*x^6 + 126*x^5 + 20*x^4 + 117*x^3 + 88*x^2 + 61*x + 82, x^27 + 33*x^25 + 34*x^24 + 118*x^23 + 56*x^22 + 14*x^21 + 84*x^20 + 115*x^19 + 120*x^18 + 27*x^17 + 46*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 30*x^8 + 38*x^7 + 88*x^6 + 30*x^5 + 20*x^4 + 85*x^3 + 88*x^2 + 29*x + 82, x^27 + 33*x^25 + 78*x^24 + 54*x^23 + 72*x^22 + 14*x^21 + 12*x^20 + 51*x^19 + 8*x^18 + 27*x^17 + 98*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 114*x^8 + 102*x^7 + 40*x^6 + 30*x^5 + 76*x^4 + 21*x^3 + 40*x^2 + 29*x + 30, x^27 + 33*x^25 + 10*x^24 + 118*x^23 + 40*x^22 + 46*x^21 + 20*x^20 + 51*x^19 + 8*x^18 + 59*x^17 + 22*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 86*x^8 + 38*x^7 + 8*x^6 + 62*x^5 + 20*x^4 + 21*x^3 + 40*x^2 + 61*x + 74, x^27 + 33*x^25 + 126*x^24 + 38*x^23 + 24*x^22 + 62*x^21 + 124*x^20 + 67*x^19 + 56*x^18 + 107*x^17 + 34*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 34*x^8 + 22*x^7 + 56*x^6 + 14*x^5 + 124*x^4 + 101*x^3 + 24*x^2 + 45*x + 126, x^27 + 33*x^25 + 62*x^24 + 22*x^23 + 40*x^22 + 46*x^21 + 76*x^20 + 83*x^19 + 40*x^18 + 123*x^17 + 18*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 66*x^8 + 70*x^7 + 8*x^6 + 62*x^5 + 12*x^4 + 53*x^3 + 72*x^2 + 125*x + 46, x^27 + 33*x^25 + 26*x^24 + 118*x^23 + 104*x^22 + 46*x^21 + 52*x^20 + 51*x^19 + 72*x^18 + 59*x^17 + 6*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 70*x^8 + 38*x^7 + 72*x^6 + 62*x^5 + 52*x^4 + 21*x^3 + 104*x^2 + 61*x + 90, x^27 + 33*x^25 + 6*x^24 + 38*x^23 + 72*x^22 + 30*x^21 + 60*x^20 + 3*x^19 + 8*x^18 + 75*x^17 + 42*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 58*x^8 + 22*x^7 + 40*x^6 + 110*x^5 + 124*x^4 + 37*x^3 + 40*x^2 + 13*x + 86, x^27 + 33*x^25 + 38*x^24 + 102*x^23 + 104*x^22 + 30*x^21 + 92*x^20 + 67*x^19 + 104*x^18 + 75*x^17 + 42*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 90*x^8 + 86*x^7 + 72*x^6 + 110*x^5 + 28*x^4 + 101*x^3 + 8*x^2 + 13*x + 22, x^27 + 33*x^25 + 54*x^24 + 38*x^23 + 40*x^22 + 94*x^21 + 124*x^20 + 3*x^19 + 40*x^18 + 11*x^17 + 26*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 74*x^8 + 22*x^7 + 8*x^6 + 46*x^5 + 60*x^4 + 37*x^3 + 72*x^2 + 77*x + 38, x^27 + 33*x^25 + 30*x^24 + 38*x^23 + 24*x^22 + 126*x^21 + 124*x^20 + 67*x^19 + 56*x^18 + 43*x^17 + 66*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 2*x^8 + 22*x^7 + 56*x^6 + 78*x^5 + 124*x^4 + 101*x^3 + 24*x^2 + 109*x + 94, x^27 + 33*x^25 + 6*x^24 + 6*x^23 + 104*x^22 + 62*x^21 + 28*x^20 + 35*x^19 + 104*x^18 + 43*x^17 + 74*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 122*x^8 + 118*x^7 + 72*x^6 + 14*x^5 + 92*x^4 + 69*x^3 + 8*x^2 + 109*x + 118, x^27 + 33*x^25 + 70*x^24 + 22*x^23 + 56*x^22 + 78*x^21 + 44*x^20 + 19*x^19 + 24*x^18 + 27*x^17 + 122*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 26*x^8 + 70*x^7 + 88*x^6 + 94*x^5 + 44*x^4 + 117*x^3 + 120*x^2 + 29*x + 102, x^27 + 33*x^25 + 94*x^24 + 118*x^23 + 72*x^22 + 78*x^21 + 108*x^20 + 115*x^19 + 8*x^18 + 91*x^17 + 18*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 98*x^8 + 38*x^7 + 40*x^6 + 94*x^5 + 44*x^4 + 85*x^3 + 40*x^2 + 93*x + 110, x^27 + 33*x^25 + 50*x^24 + 22*x^23 + 56*x^22 + 110*x^21 + 116*x^20 + 83*x^19 + 120*x^18 + 59*x^17 + 30*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 14*x^8 + 70*x^7 + 88*x^6 + 126*x^5 + 52*x^4 + 53*x^3 + 88*x^2 + 61*x + 98, x^27 + 33*x^25 + 30*x^24 + 102*x^23 + 24*x^22 + 62*x^21 + 124*x^20 + 3*x^19 + 56*x^18 + 107*x^17 + 66*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 2*x^8 + 86*x^7 + 56*x^6 + 14*x^5 + 124*x^4 + 37*x^3 + 24*x^2 + 45*x + 94, x^27 + 33*x^25 + 26*x^24 + 38*x^23 + 24*x^22 + 30*x^21 + 100*x^20 + 3*x^19 + 24*x^18 + 75*x^17 + 86*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 102*x^8 + 22*x^7 + 56*x^6 + 110*x^5 + 36*x^4 + 37*x^3 + 120*x^2 + 13*x + 106, x^27 + 33*x^25 + 66*x^24 + 6*x^23 + 72*x^22 + 30*x^21 + 100*x^20 + 99*x^19 + 104*x^18 + 11*x^17 + 62*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 94*x^8 + 118*x^7 + 40*x^6 + 110*x^5 + 100*x^4 + 5*x^3 + 8*x^2 + 77*x + 98, x^27 + 33*x^25 + 26*x^24 + 118*x^23 + 8*x^22 + 46*x^21 + 84*x^20 + 51*x^19 + 40*x^18 + 59*x^17 + 102*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 6*x^8 + 38*x^7 + 104*x^6 + 62*x^5 + 84*x^4 + 21*x^3 + 72*x^2 + 61*x + 58, x^27 + 33*x^25 + 90*x^24 + 22*x^23 + 8*x^22 + 78*x^21 + 84*x^20 + 19*x^19 + 40*x^18 + 27*x^17 + 38*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 70*x^8 + 70*x^7 + 104*x^6 + 94*x^5 + 84*x^4 + 117*x^3 + 72*x^2 + 29*x + 122, x^27 + 33*x^25 + 70*x^24 + 86*x^23 + 88*x^22 + 78*x^21 + 12*x^20 + 83*x^19 + 120*x^18 + 27*x^17 + 26*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 90*x^8 + 6*x^7 + 120*x^6 + 94*x^5 + 12*x^4 + 53*x^3 + 88*x^2 + 29*x + 6, x^27 + 33*x^25 + 110*x^24 + 22*x^23 + 104*x^22 + 46*x^21 + 44*x^20 + 83*x^19 + 104*x^18 + 123*x^17 + 98*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 18*x^8 + 70*x^7 + 72*x^6 + 62*x^5 + 108*x^4 + 53*x^3 + 8*x^2 + 125*x + 94, x^27 + 33*x^25 + 70*x^24 + 38*x^23 + 104*x^22 + 30*x^21 + 92*x^20 + 3*x^19 + 104*x^18 + 75*x^17 + 74*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 58*x^8 + 22*x^7 + 72*x^6 + 110*x^5 + 28*x^4 + 37*x^3 + 8*x^2 + 13*x + 118, x^27 + 33*x^25 + 118*x^24 + 22*x^23 + 56*x^22 + 14*x^21 + 12*x^20 + 19*x^19 + 24*x^18 + 91*x^17 + 74*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 106*x^8 + 70*x^7 + 88*x^6 + 30*x^5 + 12*x^4 + 117*x^3 + 120*x^2 + 93*x + 22, x^27 + 33*x^25 + 106*x^24 + 102*x^23 + 120*x^22 + 30*x^21 + 100*x^20 + 67*x^19 + 56*x^18 + 75*x^17 + 38*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 86*x^8 + 86*x^7 + 24*x^6 + 110*x^5 + 36*x^4 + 101*x^3 + 24*x^2 + 13*x + 90, x^27 + 33*x^25 + 86*x^24 + 118*x^23 + 24*x^22 + 110*x^21 + 44*x^20 + 51*x^19 + 56*x^18 + 123*x^17 + 10*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 74*x^8 + 38*x^7 + 56*x^6 + 126*x^5 + 44*x^4 + 21*x^3 + 24*x^2 + 125*x + 22, x^27 + 33*x^25 + 106*x^24 + 22*x^23 + 104*x^22 + 78*x^21 + 20*x^20 + 19*x^19 + 72*x^18 + 27*x^17 + 118*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 118*x^8 + 70*x^7 + 72*x^6 + 94*x^5 + 20*x^4 + 117*x^3 + 104*x^2 + 29*x + 106, x^27 + 33*x^25 + 38*x^24 + 22*x^23 + 120*x^22 + 14*x^21 + 108*x^20 + 19*x^19 + 88*x^18 + 91*x^17 + 26*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 58*x^8 + 70*x^7 + 24*x^6 + 30*x^5 + 108*x^4 + 117*x^3 + 56*x^2 + 93*x + 70, x^27 + 33*x^25 + 74*x^24 + 38*x^23 + 56*x^22 + 30*x^21 + 36*x^20 + 3*x^19 + 120*x^18 + 75*x^17 + 70*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 118*x^8 + 22*x^7 + 88*x^6 + 110*x^5 + 100*x^4 + 37*x^3 + 88*x^2 + 13*x + 58, x^27 + 33*x^25 + 6*x^24 + 118*x^23 + 88*x^22 + 110*x^21 + 12*x^20 + 51*x^19 + 120*x^18 + 123*x^17 + 90*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 26*x^8 + 38*x^7 + 120*x^6 + 126*x^5 + 12*x^4 + 21*x^3 + 88*x^2 + 125*x + 70, x^27 + 33*x^25 + 14*x^24 + 54*x^23 + 104*x^22 + 78*x^21 + 108*x^20 + 51*x^19 + 104*x^18 + 91*x^17 + 66*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 114*x^8 + 102*x^7 + 72*x^6 + 94*x^5 + 44*x^4 + 21*x^3 + 8*x^2 + 93*x + 126, x^27 + 33*x^25 + 78*x^24 + 118*x^23 + 40*x^22 + 14*x^21 + 44*x^20 + 115*x^19 + 40*x^18 + 27*x^17 + 66*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 50*x^8 + 38*x^7 + 8*x^6 + 30*x^5 + 108*x^4 + 85*x^3 + 72*x^2 + 29*x + 126, x^27 + 33*x^25 + 42*x^24 + 22*x^23 + 8*x^22 + 78*x^21 + 52*x^20 + 19*x^19 + 40*x^18 + 27*x^17 + 22*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 118*x^8 + 70*x^7 + 104*x^6 + 94*x^5 + 52*x^4 + 117*x^3 + 72*x^2 + 29*x + 10, x^27 + 33*x^25 + 54*x^24 + 38*x^23 + 104*x^22 + 94*x^21 + 60*x^20 + 3*x^19 + 104*x^18 + 11*x^17 + 90*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 74*x^8 + 22*x^7 + 72*x^6 + 46*x^5 + 124*x^4 + 37*x^3 + 8*x^2 + 77*x + 102, x^27 + 33*x^25 + 122*x^24 + 102*x^23 + 24*x^22 + 94*x^21 + 36*x^20 + 67*x^19 + 24*x^18 + 11*x^17 + 118*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 6*x^8 + 86*x^7 + 56*x^6 + 46*x^5 + 100*x^4 + 101*x^3 + 120*x^2 + 77*x + 74, x^27 + 33*x^25 + 18*x^24 + 70*x^23 + 72*x^22 + 30*x^21 + 4*x^20 + 35*x^19 + 104*x^18 + 11*x^17 + 110*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 14*x^8 + 54*x^7 + 40*x^6 + 110*x^5 + 4*x^4 + 69*x^3 + 8*x^2 + 77*x + 50, x^27 + 33*x^25 + 22*x^24 + 70*x^23 + 72*x^22 + 62*x^21 + 28*x^20 + 99*x^19 + 8*x^18 + 43*x^17 + 90*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 42*x^8 + 54*x^7 + 40*x^6 + 14*x^5 + 92*x^4 + 5*x^3 + 40*x^2 + 109*x + 38, x^27 + 33*x^25 + 106*x^24 + 70*x^23 + 120*x^22 + 62*x^21 + 36*x^20 + 99*x^19 + 56*x^18 + 43*x^17 + 102*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 86*x^8 + 54*x^7 + 24*x^6 + 14*x^5 + 100*x^4 + 5*x^3 + 24*x^2 + 109*x + 26, x^27 + 33*x^25 + 14*x^24 + 6*x^23 + 24*x^22 + 30*x^21 + 92*x^20 + 99*x^19 + 56*x^18 + 11*x^17 + 82*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 18*x^8 + 118*x^7 + 56*x^6 + 110*x^5 + 92*x^4 + 5*x^3 + 24*x^2 + 77*x + 78, x^27 + 33*x^25 + 114*x^24 + 6*x^23 + 8*x^22 + 30*x^21 + 68*x^20 + 99*x^19 + 40*x^18 + 11*x^17 + 14*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 46*x^8 + 118*x^7 + 104*x^6 + 110*x^5 + 68*x^4 + 5*x^3 + 72*x^2 + 77*x + 18, x^27 + 33*x^25 + 10*x^24 + 38*x^23 + 24*x^22 + 30*x^21 + 4*x^20 + 3*x^19 + 24*x^18 + 75*x^17 + 38*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 118*x^8 + 22*x^7 + 56*x^6 + 110*x^5 + 68*x^4 + 37*x^3 + 120*x^2 + 13*x + 26, x^27 + 33*x^25 + 66*x^24 + 38*x^23 + 40*x^22 + 62*x^21 + 68*x^20 + 67*x^19 + 8*x^18 + 107*x^17 + 94*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 30*x^8 + 22*x^7 + 8*x^6 + 14*x^5 + 68*x^4 + 101*x^3 + 40*x^2 + 45*x + 2, x^27 + 33*x^25 + 110*x^24 + 102*x^23 + 24*x^22 + 62*x^21 + 92*x^20 + 3*x^19 + 56*x^18 + 107*x^17 + 50*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 50*x^8 + 86*x^7 + 56*x^6 + 14*x^5 + 92*x^4 + 37*x^3 + 24*x^2 + 45*x + 110, x^27 + 33*x^25 + 38*x^24 + 118*x^23 + 120*x^22 + 110*x^21 + 108*x^20 + 51*x^19 + 88*x^18 + 123*x^17 + 26*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 58*x^8 + 38*x^7 + 24*x^6 + 126*x^5 + 108*x^4 + 21*x^3 + 56*x^2 + 125*x + 70, x^27 + 33*x^25 + 22*x^24 + 22*x^23 + 56*x^22 + 14*x^21 + 76*x^20 + 19*x^19 + 24*x^18 + 91*x^17 + 42*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 74*x^8 + 70*x^7 + 88*x^6 + 30*x^5 + 76*x^4 + 117*x^3 + 120*x^2 + 93*x + 54, x^27 + 33*x^25 + 50*x^24 + 102*x^23 + 40*x^22 + 126*x^21 + 100*x^20 + 3*x^19 + 8*x^18 + 43*x^17 + 46*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 46*x^8 + 86*x^7 + 8*x^6 + 78*x^5 + 100*x^4 + 37*x^3 + 40*x^2 + 109*x + 50, x^27 + 33*x^25 + 122*x^24 + 118*x^23 + 8*x^22 + 46*x^21 + 20*x^20 + 51*x^19 + 40*x^18 + 59*x^17 + 6*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 38*x^8 + 38*x^7 + 104*x^6 + 62*x^5 + 20*x^4 + 21*x^3 + 72*x^2 + 61*x + 26, x^27 + 33*x^25 + 90*x^24 + 54*x^23 + 8*x^22 + 46*x^21 + 20*x^20 + 115*x^19 + 40*x^18 + 59*x^17 + 102*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 70*x^8 + 102*x^7 + 104*x^6 + 62*x^5 + 20*x^4 + 85*x^3 + 72*x^2 + 61*x + 58, x^27 + 33*x^25 + 10*x^24 + 70*x^23 + 88*x^22 + 62*x^21 + 68*x^20 + 99*x^19 + 88*x^18 + 43*x^17 + 102*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 118*x^8 + 54*x^7 + 120*x^6 + 14*x^5 + 4*x^4 + 5*x^3 + 56*x^2 + 109*x + 90, x^27 + 33*x^25 + 50*x^24 + 22*x^23 + 24*x^22 + 110*x^21 + 84*x^20 + 83*x^19 + 24*x^18 + 59*x^17 + 62*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 78*x^8 + 70*x^7 + 56*x^6 + 126*x^5 + 20*x^4 + 53*x^3 + 120*x^2 + 61*x + 2, x^27 + 33*x^25 + 62*x^24 + 70*x^23 + 120*x^22 + 94*x^21 + 92*x^20 + 35*x^19 + 88*x^18 + 75*x^17 + 2*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 34*x^8 + 54*x^7 + 24*x^6 + 46*x^5 + 92*x^4 + 69*x^3 + 56*x^2 + 13*x + 94, x^27 + 33*x^25 + 110*x^24 + 22*x^23 + 104*x^22 + 110*x^21 + 108*x^20 + 83*x^19 + 104*x^18 + 59*x^17 + 34*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 18*x^8 + 70*x^7 + 72*x^6 + 126*x^5 + 44*x^4 + 53*x^3 + 8*x^2 + 61*x + 30, x^27 + 33*x^25 + 10*x^24 + 70*x^23 + 56*x^22 + 62*x^21 + 36*x^20 + 99*x^19 + 120*x^18 + 43*x^17 + 6*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 54*x^8 + 54*x^7 + 88*x^6 + 14*x^5 + 100*x^4 + 5*x^3 + 88*x^2 + 109*x + 122, x^27 + 33*x^25 + 34*x^24 + 86*x^23 + 88*x^22 + 46*x^21 + 52*x^20 + 19*x^19 + 88*x^18 + 123*x^17 + 78*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 94*x^8 + 6*x^7 + 120*x^6 + 62*x^5 + 116*x^4 + 117*x^3 + 56*x^2 + 125*x + 114, x^27 + 33*x^25 + 98*x^24 + 54*x^23 + 24*x^22 + 14*x^21 + 116*x^20 + 51*x^19 + 24*x^18 + 27*x^17 + 78*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 30*x^8 + 102*x^7 + 56*x^6 + 30*x^5 + 52*x^4 + 21*x^3 + 120*x^2 + 29*x + 114, x^27 + 33*x^25 + 70*x^24 + 70*x^23 + 104*x^22 + 62*x^21 + 92*x^20 + 99*x^19 + 104*x^18 + 43*x^17 + 74*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 58*x^8 + 54*x^7 + 72*x^6 + 14*x^5 + 28*x^4 + 5*x^3 + 8*x^2 + 109*x + 118, x^27 + 33*x^25 + 58*x^24 + 54*x^23 + 104*x^22 + 46*x^21 + 52*x^20 + 115*x^19 + 72*x^18 + 59*x^17 + 38*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 38*x^8 + 102*x^7 + 72*x^6 + 62*x^5 + 52*x^4 + 85*x^3 + 104*x^2 + 61*x + 58, x^27 + 33*x^25 + 94*x^24 + 118*x^23 + 72*x^22 + 14*x^21 + 44*x^20 + 115*x^19 + 8*x^18 + 27*x^17 + 82*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 98*x^8 + 38*x^7 + 40*x^6 + 30*x^5 + 108*x^4 + 85*x^3 + 40*x^2 + 29*x + 46, x^27 + 33*x^25 + 14*x^24 + 6*x^23 + 88*x^22 + 94*x^21 + 92*x^20 + 99*x^19 + 120*x^18 + 75*x^17 + 82*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 18*x^8 + 118*x^7 + 120*x^6 + 46*x^5 + 92*x^4 + 5*x^3 + 88*x^2 + 13*x + 78, x^27 + 33*x^25 + 94*x^24 + 86*x^23 + 72*x^22 + 46*x^21 + 108*x^20 + 19*x^19 + 8*x^18 + 123*x^17 + 18*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 98*x^8 + 6*x^7 + 40*x^6 + 62*x^5 + 44*x^4 + 117*x^3 + 40*x^2 + 125*x + 110, x^27 + 33*x^25 + 6*x^24 + 118*x^23 + 120*x^22 + 46*x^21 + 108*x^20 + 51*x^19 + 88*x^18 + 59*x^17 + 122*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 90*x^8 + 38*x^7 + 24*x^6 + 62*x^5 + 108*x^4 + 21*x^3 + 56*x^2 + 61*x + 102, x^27 + 33*x^25 + 18*x^24 + 70*x^23 + 72*x^22 + 94*x^21 + 68*x^20 + 35*x^19 + 104*x^18 + 75*x^17 + 46*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 14*x^8 + 54*x^7 + 40*x^6 + 46*x^5 + 68*x^4 + 69*x^3 + 8*x^2 + 13*x + 114, x^27 + 33*x^25 + 102*x^24 + 102*x^23 + 40*x^22 + 30*x^21 + 28*x^20 + 67*x^19 + 40*x^18 + 75*x^17 + 42*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 26*x^8 + 86*x^7 + 8*x^6 + 110*x^5 + 92*x^4 + 101*x^3 + 72*x^2 + 13*x + 22, x^27 + 33*x^25 + 18*x^24 + 102*x^23 + 40*x^22 + 126*x^21 + 36*x^20 + 3*x^19 + 8*x^18 + 43*x^17 + 78*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 78*x^8 + 86*x^7 + 8*x^6 + 78*x^5 + 36*x^4 + 37*x^3 + 40*x^2 + 109*x + 18, x^27 + 33*x^25 + 70*x^24 + 118*x^23 + 88*x^22 + 110*x^21 + 12*x^20 + 51*x^19 + 120*x^18 + 123*x^17 + 26*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 90*x^8 + 38*x^7 + 120*x^6 + 126*x^5 + 12*x^4 + 21*x^3 + 88*x^2 + 125*x + 6, x^27 + 33*x^25 + 30*x^24 + 118*x^23 + 8*x^22 + 78*x^21 + 44*x^20 + 115*x^19 + 72*x^18 + 91*x^17 + 18*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 34*x^8 + 38*x^7 + 104*x^6 + 94*x^5 + 108*x^4 + 85*x^3 + 104*x^2 + 93*x + 110, x^27 + 33*x^25 + 10*x^24 + 22*x^23 + 8*x^22 + 14*x^21 + 52*x^20 + 19*x^19 + 40*x^18 + 91*x^17 + 118*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 22*x^8 + 70*x^7 + 104*x^6 + 30*x^5 + 52*x^4 + 117*x^3 + 72*x^2 + 93*x + 42, x^27 + 33*x^25 + 110*x^24 + 70*x^23 + 24*x^22 + 94*x^21 + 28*x^20 + 35*x^19 + 56*x^18 + 75*x^17 + 114*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 50*x^8 + 54*x^7 + 56*x^6 + 46*x^5 + 28*x^4 + 69*x^3 + 24*x^2 + 13*x + 46, x^27 + 33*x^25 + 90*x^24 + 22*x^23 + 40*x^22 + 14*x^21 + 52*x^20 + 19*x^19 + 8*x^18 + 91*x^17 + 70*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 6*x^8 + 70*x^7 + 8*x^6 + 30*x^5 + 52*x^4 + 117*x^3 + 40*x^2 + 93*x + 26, x^27 + 33*x^25 + 42*x^24 + 22*x^23 + 104*x^22 + 78*x^21 + 20*x^20 + 19*x^19 + 72*x^18 + 27*x^17 + 54*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 54*x^8 + 70*x^7 + 72*x^6 + 94*x^5 + 20*x^4 + 117*x^3 + 104*x^2 + 29*x + 42, x^27 + 33*x^25 + 86*x^24 + 118*x^23 + 120*x^22 + 46*x^21 + 76*x^20 + 51*x^19 + 88*x^18 + 59*x^17 + 106*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 10*x^8 + 38*x^7 + 24*x^6 + 62*x^5 + 76*x^4 + 21*x^3 + 56*x^2 + 61*x + 118, x^27 + 33*x^25 + 22*x^24 + 86*x^23 + 56*x^22 + 78*x^21 + 76*x^20 + 83*x^19 + 24*x^18 + 27*x^17 + 42*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 74*x^8 + 6*x^7 + 88*x^6 + 94*x^5 + 76*x^4 + 53*x^3 + 120*x^2 + 29*x + 54, x^27 + 33*x^25 + 126*x^24 + 70*x^23 + 56*x^22 + 94*x^21 + 28*x^20 + 35*x^19 + 24*x^18 + 75*x^17 + 2*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 98*x^8 + 54*x^7 + 88*x^6 + 46*x^5 + 28*x^4 + 69*x^3 + 120*x^2 + 13*x + 94, x^27 + 33*x^25 + 122*x^24 + 38*x^23 + 24*x^22 + 30*x^21 + 36*x^20 + 3*x^19 + 24*x^18 + 75*x^17 + 118*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 6*x^8 + 22*x^7 + 56*x^6 + 110*x^5 + 100*x^4 + 37*x^3 + 120*x^2 + 13*x + 74, x^27 + 33*x^25 + 26*x^24 + 22*x^23 + 8*x^22 + 14*x^21 + 20*x^20 + 19*x^19 + 40*x^18 + 91*x^17 + 38*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 6*x^8 + 70*x^7 + 104*x^6 + 30*x^5 + 20*x^4 + 117*x^3 + 72*x^2 + 93*x + 122, x^27 + 33*x^25 + 34*x^24 + 22*x^23 + 56*x^22 + 110*x^21 + 20*x^20 + 83*x^19 + 120*x^18 + 59*x^17 + 110*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 30*x^8 + 70*x^7 + 88*x^6 + 126*x^5 + 84*x^4 + 53*x^3 + 88*x^2 + 61*x + 18, x^27 + 33*x^25 + 38*x^24 + 102*x^23 + 72*x^22 + 94*x^21 + 124*x^20 + 67*x^19 + 8*x^18 + 11*x^17 + 10*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 26*x^8 + 86*x^7 + 40*x^6 + 46*x^5 + 60*x^4 + 101*x^3 + 40*x^2 + 77*x + 118, x^27 + 33*x^25 + 6*x^24 + 22*x^23 + 120*x^22 + 78*x^21 + 108*x^20 + 19*x^19 + 88*x^18 + 27*x^17 + 122*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 90*x^8 + 70*x^7 + 24*x^6 + 94*x^5 + 108*x^4 + 117*x^3 + 56*x^2 + 29*x + 102, x^27 + 33*x^25 + 22*x^24 + 22*x^23 + 24*x^22 + 14*x^21 + 44*x^20 + 19*x^19 + 56*x^18 + 91*x^17 + 74*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 10*x^8 + 70*x^7 + 56*x^6 + 30*x^5 + 44*x^4 + 117*x^3 + 24*x^2 + 93*x + 86, x^27 + 33*x^25 + 10*x^24 + 118*x^23 + 8*x^22 + 110*x^21 + 52*x^20 + 51*x^19 + 40*x^18 + 123*x^17 + 118*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 22*x^8 + 38*x^7 + 104*x^6 + 126*x^5 + 52*x^4 + 21*x^3 + 72*x^2 + 125*x + 42, x^27 + 33*x^25 + 50*x^24 + 54*x^23 + 24*x^22 + 14*x^21 + 84*x^20 + 51*x^19 + 24*x^18 + 27*x^17 + 62*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 78*x^8 + 102*x^7 + 56*x^6 + 30*x^5 + 20*x^4 + 21*x^3 + 120*x^2 + 29*x + 2, x^27 + 33*x^25 + 14*x^24 + 54*x^23 + 72*x^22 + 14*x^21 + 12*x^20 + 51*x^19 + 8*x^18 + 27*x^17 + 34*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 50*x^8 + 102*x^7 + 40*x^6 + 30*x^5 + 76*x^4 + 21*x^3 + 40*x^2 + 29*x + 94, x^27 + 33*x^25 + 118*x^24 + 70*x^23 + 72*x^22 + 62*x^21 + 92*x^20 + 99*x^19 + 8*x^18 + 43*x^17 + 122*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 74*x^8 + 54*x^7 + 40*x^6 + 14*x^5 + 28*x^4 + 5*x^3 + 40*x^2 + 109*x + 6, x^27 + 33*x^25 + 78*x^24 + 54*x^23 + 8*x^22 + 14*x^21 + 76*x^20 + 51*x^19 + 72*x^18 + 27*x^17 + 34*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 114*x^8 + 102*x^7 + 104*x^6 + 30*x^5 + 12*x^4 + 21*x^3 + 104*x^2 + 29*x + 94, x^27 + 33*x^25 + 86*x^24 + 102*x^23 + 104*x^22 + 30*x^21 + 124*x^20 + 67*x^19 + 104*x^18 + 75*x^17 + 58*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 42*x^8 + 86*x^7 + 72*x^6 + 110*x^5 + 60*x^4 + 101*x^3 + 8*x^2 + 13*x + 6, x^27 + 33*x^25 + 98*x^24 + 86*x^23 + 120*x^22 + 46*x^21 + 84*x^20 + 19*x^19 + 56*x^18 + 123*x^17 + 110*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 94*x^8 + 6*x^7 + 24*x^6 + 62*x^5 + 20*x^4 + 117*x^3 + 24*x^2 + 125*x + 18, x^27 + 33*x^25 + 94*x^24 + 102*x^23 + 120*x^22 + 126*x^21 + 28*x^20 + 3*x^19 + 88*x^18 + 43*x^17 + 98*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 2*x^8 + 86*x^7 + 24*x^6 + 78*x^5 + 28*x^4 + 37*x^3 + 56*x^2 + 109*x + 126, x^27 + 33*x^25 + 90*x^24 + 118*x^23 + 8*x^22 + 46*x^21 + 84*x^20 + 51*x^19 + 40*x^18 + 59*x^17 + 38*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 70*x^8 + 38*x^7 + 104*x^6 + 62*x^5 + 84*x^4 + 21*x^3 + 72*x^2 + 61*x + 122, x^27 + 33*x^25 + 26*x^24 + 54*x^23 + 8*x^22 + 46*x^21 + 20*x^20 + 115*x^19 + 40*x^18 + 59*x^17 + 38*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 6*x^8 + 102*x^7 + 104*x^6 + 62*x^5 + 20*x^4 + 85*x^3 + 72*x^2 + 61*x + 122, x^27 + 33*x^25 + 118*x^24 + 38*x^23 + 40*x^22 + 94*x^21 + 124*x^20 + 3*x^19 + 40*x^18 + 11*x^17 + 90*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 10*x^8 + 22*x^7 + 8*x^6 + 46*x^5 + 60*x^4 + 37*x^3 + 72*x^2 + 77*x + 102, x^27 + 33*x^25 + 82*x^24 + 6*x^23 + 72*x^22 + 94*x^21 + 4*x^20 + 99*x^19 + 104*x^18 + 75*x^17 + 46*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 78*x^8 + 118*x^7 + 40*x^6 + 46*x^5 + 4*x^4 + 5*x^3 + 8*x^2 + 13*x + 114, x^27 + 33*x^25 + 106*x^24 + 102*x^23 + 88*x^22 + 94*x^21 + 4*x^20 + 67*x^19 + 88*x^18 + 11*x^17 + 6*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 22*x^8 + 86*x^7 + 120*x^6 + 46*x^5 + 68*x^4 + 101*x^3 + 56*x^2 + 77*x + 58, x^27 + 33*x^25 + 54*x^24 + 70*x^23 + 40*x^22 + 126*x^21 + 124*x^20 + 99*x^19 + 40*x^18 + 107*x^17 + 26*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 74*x^8 + 54*x^7 + 8*x^6 + 78*x^5 + 60*x^4 + 5*x^3 + 72*x^2 + 45*x + 38, x^27 + 33*x^25 + 58*x^24 + 6*x^23 + 56*x^22 + 126*x^21 + 68*x^20 + 35*x^19 + 120*x^18 + 107*x^17 + 22*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 6*x^8 + 118*x^7 + 88*x^6 + 78*x^5 + 4*x^4 + 69*x^3 + 88*x^2 + 45*x + 106, x^27 + 33*x^25 + 118*x^24 + 70*x^23 + 8*x^22 + 62*x^21 + 28*x^20 + 99*x^19 + 72*x^18 + 43*x^17 + 58*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 74*x^8 + 54*x^7 + 104*x^6 + 14*x^5 + 92*x^4 + 5*x^3 + 104*x^2 + 109*x + 70, x^27 + 33*x^25 + 22*x^24 + 118*x^23 + 24*x^22 + 110*x^21 + 44*x^20 + 51*x^19 + 56*x^18 + 123*x^17 + 74*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 10*x^8 + 38*x^7 + 56*x^6 + 126*x^5 + 44*x^4 + 21*x^3 + 24*x^2 + 125*x + 86, x^27 + 33*x^25 + 26*x^24 + 102*x^23 + 56*x^22 + 30*x^21 + 68*x^20 + 67*x^19 + 120*x^18 + 75*x^17 + 118*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 38*x^8 + 86*x^7 + 88*x^6 + 110*x^5 + 4*x^4 + 101*x^3 + 88*x^2 + 13*x + 10, x^27 + 33*x^25 + 110*x^24 + 38*x^23 + 120*x^22 + 62*x^21 + 124*x^20 + 67*x^19 + 88*x^18 + 107*x^17 + 18*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 114*x^8 + 22*x^7 + 24*x^6 + 14*x^5 + 124*x^4 + 101*x^3 + 56*x^2 + 45*x + 78, x^27 + 33*x^25 + 6*x^24 + 86*x^23 + 88*x^22 + 14*x^21 + 76*x^20 + 83*x^19 + 120*x^18 + 91*x^17 + 26*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 26*x^8 + 6*x^7 + 120*x^6 + 30*x^5 + 76*x^4 + 53*x^3 + 88*x^2 + 93*x + 6, x^27 + 33*x^25 + 74*x^24 + 70*x^23 + 24*x^22 + 62*x^21 + 4*x^20 + 99*x^19 + 24*x^18 + 43*x^17 + 102*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 54*x^8 + 54*x^7 + 56*x^6 + 14*x^5 + 68*x^4 + 5*x^3 + 120*x^2 + 109*x + 90, x^27 + 33*x^25 + 26*x^24 + 86*x^23 + 104*x^22 + 14*x^21 + 52*x^20 + 83*x^19 + 72*x^18 + 91*x^17 + 6*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 70*x^8 + 6*x^7 + 72*x^6 + 30*x^5 + 52*x^4 + 53*x^3 + 104*x^2 + 93*x + 90, x^27 + 33*x^25 + 110*x^24 + 118*x^23 + 72*x^22 + 78*x^21 + 76*x^20 + 115*x^19 + 8*x^18 + 91*x^17 + 66*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 82*x^8 + 38*x^7 + 40*x^6 + 94*x^5 + 12*x^4 + 85*x^3 + 40*x^2 + 93*x + 62, x^27 + 33*x^25 + 78*x^24 + 22*x^23 + 40*x^22 + 46*x^21 + 44*x^20 + 83*x^19 + 40*x^18 + 123*x^17 + 66*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 50*x^8 + 70*x^7 + 8*x^6 + 62*x^5 + 108*x^4 + 53*x^3 + 72*x^2 + 125*x + 126, x^27 + 33*x^25 + 90*x^24 + 70*x^23 + 120*x^22 + 126*x^21 + 4*x^20 + 99*x^19 + 56*x^18 + 107*x^17 + 118*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 102*x^8 + 54*x^7 + 24*x^6 + 78*x^5 + 68*x^4 + 5*x^3 + 24*x^2 + 45*x + 10, x^27 + 33*x^25 + 26*x^24 + 102*x^23 + 120*x^22 + 94*x^21 + 68*x^20 + 67*x^19 + 56*x^18 + 11*x^17 + 118*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 38*x^8 + 86*x^7 + 24*x^6 + 46*x^5 + 4*x^4 + 101*x^3 + 24*x^2 + 77*x + 10, x^27 + 33*x^25 + 54*x^24 + 118*x^23 + 88*x^22 + 46*x^21 + 108*x^20 + 51*x^19 + 120*x^18 + 59*x^17 + 42*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 106*x^8 + 38*x^7 + 120*x^6 + 62*x^5 + 108*x^4 + 21*x^3 + 88*x^2 + 61*x + 118, x^27 + 33*x^25 + 102*x^24 + 70*x^23 + 40*x^22 + 126*x^21 + 28*x^20 + 99*x^19 + 40*x^18 + 107*x^17 + 42*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 26*x^8 + 54*x^7 + 8*x^6 + 78*x^5 + 92*x^4 + 5*x^3 + 72*x^2 + 45*x + 22, x^27 + 33*x^25 + 26*x^24 + 86*x^23 + 8*x^22 + 78*x^21 + 20*x^20 + 83*x^19 + 40*x^18 + 27*x^17 + 38*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 6*x^8 + 6*x^7 + 104*x^6 + 94*x^5 + 20*x^4 + 53*x^3 + 72*x^2 + 29*x + 122, x^27 + 33*x^25 + 98*x^24 + 70*x^23 + 8*x^22 + 30*x^21 + 36*x^20 + 35*x^19 + 40*x^18 + 11*x^17 + 30*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 62*x^8 + 54*x^7 + 104*x^6 + 110*x^5 + 36*x^4 + 69*x^3 + 72*x^2 + 77*x + 2, x^27 + 33*x^25 + 10*x^24 + 54*x^23 + 40*x^22 + 46*x^21 + 84*x^20 + 115*x^19 + 8*x^18 + 59*x^17 + 86*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 86*x^8 + 102*x^7 + 8*x^6 + 62*x^5 + 84*x^4 + 85*x^3 + 40*x^2 + 61*x + 10, x^27 + 33*x^25 + 86*x^24 + 102*x^23 + 104*x^22 + 94*x^21 + 60*x^20 + 67*x^19 + 104*x^18 + 11*x^17 + 122*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 42*x^8 + 86*x^7 + 72*x^6 + 46*x^5 + 124*x^4 + 101*x^3 + 8*x^2 + 77*x + 70, x^27 + 33*x^25 + 22*x^24 + 86*x^23 + 24*x^22 + 78*x^21 + 44*x^20 + 83*x^19 + 56*x^18 + 27*x^17 + 74*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 10*x^8 + 6*x^7 + 56*x^6 + 94*x^5 + 44*x^4 + 53*x^3 + 24*x^2 + 29*x + 86, x^27 + 33*x^25 + 62*x^24 + 22*x^23 + 104*x^22 + 110*x^21 + 76*x^20 + 83*x^19 + 104*x^18 + 59*x^17 + 18*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 66*x^8 + 70*x^7 + 72*x^6 + 126*x^5 + 12*x^4 + 53*x^3 + 8*x^2 + 61*x + 46, x^27 + 33*x^25 + 30*x^24 + 86*x^23 + 8*x^22 + 46*x^21 + 44*x^20 + 19*x^19 + 72*x^18 + 123*x^17 + 18*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 34*x^8 + 6*x^7 + 104*x^6 + 62*x^5 + 108*x^4 + 117*x^3 + 104*x^2 + 125*x + 110, x^27 + 33*x^25 + 98*x^24 + 22*x^23 + 24*x^22 + 110*x^21 + 116*x^20 + 83*x^19 + 24*x^18 + 59*x^17 + 78*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 30*x^8 + 70*x^7 + 56*x^6 + 126*x^5 + 52*x^4 + 53*x^3 + 120*x^2 + 61*x + 114, x^27 + 33*x^25 + 90*x^24 + 6*x^23 + 120*x^22 + 126*x^21 + 68*x^20 + 35*x^19 + 56*x^18 + 107*x^17 + 54*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 102*x^8 + 118*x^7 + 24*x^6 + 78*x^5 + 4*x^4 + 69*x^3 + 24*x^2 + 45*x + 74, x^27 + 33*x^25 + 34*x^24 + 70*x^23 + 72*x^22 + 30*x^21 + 100*x^20 + 35*x^19 + 104*x^18 + 11*x^17 + 30*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 126*x^8 + 54*x^7 + 40*x^6 + 110*x^5 + 100*x^4 + 69*x^3 + 8*x^2 + 77*x + 2, x^27 + 33*x^25 + 86*x^24 + 70*x^23 + 72*x^22 + 62*x^21 + 28*x^20 + 99*x^19 + 8*x^18 + 43*x^17 + 26*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 106*x^8 + 54*x^7 + 40*x^6 + 14*x^5 + 92*x^4 + 5*x^3 + 40*x^2 + 109*x + 102, x^27 + 33*x^25 + 18*x^24 + 86*x^23 + 120*x^22 + 46*x^21 + 116*x^20 + 19*x^19 + 56*x^18 + 123*x^17 + 126*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 46*x^8 + 6*x^7 + 24*x^6 + 62*x^5 + 52*x^4 + 117*x^3 + 24*x^2 + 125*x + 2, x^27 + 33*x^25 + 34*x^24 + 118*x^23 + 24*x^22 + 14*x^21 + 52*x^20 + 115*x^19 + 24*x^18 + 27*x^17 + 78*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 94*x^8 + 38*x^7 + 56*x^6 + 30*x^5 + 116*x^4 + 85*x^3 + 120*x^2 + 29*x + 114, x^27 + 33*x^25 + 98*x^24 + 22*x^23 + 24*x^22 + 46*x^21 + 52*x^20 + 83*x^19 + 24*x^18 + 123*x^17 + 14*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 30*x^8 + 70*x^7 + 56*x^6 + 62*x^5 + 116*x^4 + 53*x^3 + 120*x^2 + 125*x + 50, x^27 + 33*x^25 + 74*x^24 + 70*x^23 + 120*x^22 + 126*x^21 + 36*x^20 + 99*x^19 + 56*x^18 + 107*x^17 + 70*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 118*x^8 + 54*x^7 + 24*x^6 + 78*x^5 + 100*x^4 + 5*x^3 + 24*x^2 + 45*x + 58, x^27 + 33*x^25 + 54*x^24 + 70*x^23 + 104*x^22 + 126*x^21 + 60*x^20 + 99*x^19 + 104*x^18 + 107*x^17 + 90*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 74*x^8 + 54*x^7 + 72*x^6 + 78*x^5 + 124*x^4 + 5*x^3 + 8*x^2 + 45*x + 102, x^27 + 33*x^25 + 66*x^24 + 22*x^23 + 120*x^22 + 46*x^21 + 84*x^20 + 83*x^19 + 56*x^18 + 123*x^17 + 78*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 126*x^8 + 70*x^7 + 24*x^6 + 62*x^5 + 20*x^4 + 53*x^3 + 24*x^2 + 125*x + 50, x^27 + 33*x^25 + 10*x^24 + 6*x^23 + 24*x^22 + 126*x^21 + 4*x^20 + 35*x^19 + 24*x^18 + 107*x^17 + 38*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 118*x^8 + 118*x^7 + 56*x^6 + 78*x^5 + 68*x^4 + 69*x^3 + 120*x^2 + 45*x + 26, x^27 + 33*x^25 + 90*x^24 + 22*x^23 + 104*x^22 + 14*x^21 + 116*x^20 + 19*x^19 + 72*x^18 + 91*x^17 + 6*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 6*x^8 + 70*x^7 + 72*x^6 + 30*x^5 + 116*x^4 + 117*x^3 + 104*x^2 + 93*x + 90, x^27 + 33*x^25 + 26*x^24 + 38*x^23 + 56*x^22 + 30*x^21 + 4*x^20 + 3*x^19 + 120*x^18 + 75*x^17 + 54*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 38*x^8 + 22*x^7 + 88*x^6 + 110*x^5 + 68*x^4 + 37*x^3 + 88*x^2 + 13*x + 74, x^27 + 33*x^25 + 30*x^24 + 6*x^23 + 88*x^22 + 30*x^21 + 124*x^20 + 99*x^19 + 120*x^18 + 11*x^17 + 66*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 2*x^8 + 118*x^7 + 120*x^6 + 110*x^5 + 124*x^4 + 5*x^3 + 88*x^2 + 77*x + 94, x^27 + 33*x^25 + 78*x^24 + 86*x^23 + 72*x^22 + 110*x^21 + 76*x^20 + 19*x^19 + 8*x^18 + 59*x^17 + 34*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 114*x^8 + 6*x^7 + 40*x^6 + 126*x^5 + 12*x^4 + 117*x^3 + 40*x^2 + 61*x + 94, x^27 + 33*x^25 + 86*x^24 + 38*x^23 + 72*x^22 + 30*x^21 + 28*x^20 + 3*x^19 + 8*x^18 + 75*x^17 + 26*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 106*x^8 + 22*x^7 + 40*x^6 + 110*x^5 + 92*x^4 + 37*x^3 + 40*x^2 + 13*x + 102, x^27 + 33*x^25 + 114*x^24 + 86*x^23 + 24*x^22 + 46*x^21 + 84*x^20 + 19*x^19 + 24*x^18 + 123*x^17 + 126*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 14*x^8 + 6*x^7 + 56*x^6 + 62*x^5 + 20*x^4 + 117*x^3 + 120*x^2 + 125*x + 66, x^27 + 33*x^25 + 58*x^24 + 118*x^23 + 72*x^22 + 110*x^21 + 20*x^20 + 51*x^19 + 104*x^18 + 123*x^17 + 70*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 102*x^8 + 38*x^7 + 40*x^6 + 126*x^5 + 20*x^4 + 21*x^3 + 8*x^2 + 125*x + 90, x^27 + 33*x^25 + 122*x^24 + 70*x^23 + 56*x^22 + 62*x^21 + 68*x^20 + 99*x^19 + 120*x^18 + 43*x^17 + 86*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 70*x^8 + 54*x^7 + 88*x^6 + 14*x^5 + 4*x^4 + 5*x^3 + 88*x^2 + 109*x + 42, x^27 + 33*x^25 + 98*x^24 + 102*x^23 + 8*x^22 + 126*x^21 + 100*x^20 + 3*x^19 + 40*x^18 + 43*x^17 + 94*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 62*x^8 + 86*x^7 + 104*x^6 + 78*x^5 + 100*x^4 + 37*x^3 + 72*x^2 + 109*x + 66, x^27 + 33*x^25 + 26*x^24 + 38*x^23 + 120*x^22 + 94*x^21 + 4*x^20 + 3*x^19 + 56*x^18 + 11*x^17 + 54*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 38*x^8 + 22*x^7 + 24*x^6 + 46*x^5 + 68*x^4 + 37*x^3 + 24*x^2 + 77*x + 74, x^27 + 33*x^25 + 86*x^24 + 70*x^23 + 8*x^22 + 126*x^21 + 28*x^20 + 99*x^19 + 72*x^18 + 107*x^17 + 26*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 106*x^8 + 54*x^7 + 104*x^6 + 78*x^5 + 92*x^4 + 5*x^3 + 104*x^2 + 45*x + 102, x^27 + 33*x^25 + 82*x^24 + 118*x^23 + 24*x^22 + 78*x^21 + 20*x^20 + 115*x^19 + 24*x^18 + 91*x^17 + 30*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 46*x^8 + 38*x^7 + 56*x^6 + 94*x^5 + 84*x^4 + 85*x^3 + 120*x^2 + 93*x + 34, x^27 + 33*x^25 + 54*x^24 + 38*x^23 + 40*x^22 + 30*x^21 + 60*x^20 + 3*x^19 + 40*x^18 + 75*x^17 + 90*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 74*x^8 + 22*x^7 + 8*x^6 + 110*x^5 + 124*x^4 + 37*x^3 + 72*x^2 + 13*x + 102, x^27 + 33*x^25 + 30*x^24 + 6*x^23 + 24*x^22 + 30*x^21 + 60*x^20 + 99*x^19 + 56*x^18 + 11*x^17 + 2*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 2*x^8 + 118*x^7 + 56*x^6 + 110*x^5 + 60*x^4 + 5*x^3 + 24*x^2 + 77*x + 30, x^27 + 33*x^25 + 42*x^24 + 102*x^23 + 88*x^22 + 30*x^21 + 68*x^20 + 67*x^19 + 88*x^18 + 75*x^17 + 6*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 86*x^8 + 86*x^7 + 120*x^6 + 110*x^5 + 4*x^4 + 101*x^3 + 56*x^2 + 13*x + 58, x^27 + 33*x^25 + 46*x^24 + 6*x^23 + 56*x^22 + 30*x^21 + 60*x^20 + 99*x^19 + 24*x^18 + 11*x^17 + 18*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 50*x^8 + 118*x^7 + 88*x^6 + 110*x^5 + 60*x^4 + 5*x^3 + 120*x^2 + 77*x + 78, x^27 + 33*x^25 + 78*x^24 + 54*x^23 + 40*x^22 + 78*x^21 + 44*x^20 + 51*x^19 + 40*x^18 + 91*x^17 + 66*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 50*x^8 + 102*x^7 + 8*x^6 + 94*x^5 + 108*x^4 + 21*x^3 + 72*x^2 + 93*x + 126, x^27 + 33*x^25 + 78*x^24 + 38*x^23 + 24*x^22 + 62*x^21 + 92*x^20 + 67*x^19 + 56*x^18 + 107*x^17 + 18*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 82*x^8 + 22*x^7 + 56*x^6 + 14*x^5 + 92*x^4 + 101*x^3 + 24*x^2 + 45*x + 14, x^27 + 33*x^25 + 58*x^24 + 22*x^23 + 72*x^22 + 78*x^21 + 84*x^20 + 19*x^19 + 104*x^18 + 27*x^17 + 6*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 102*x^8 + 70*x^7 + 40*x^6 + 94*x^5 + 84*x^4 + 117*x^3 + 8*x^2 + 29*x + 26, x^27 + 33*x^25 + 98*x^24 + 22*x^23 + 56*x^22 + 46*x^21 + 84*x^20 + 83*x^19 + 120*x^18 + 123*x^17 + 110*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 94*x^8 + 70*x^7 + 88*x^6 + 62*x^5 + 20*x^4 + 53*x^3 + 88*x^2 + 125*x + 18, x^27 + 33*x^25 + 2*x^24 + 22*x^23 + 24*x^22 + 110*x^21 + 52*x^20 + 83*x^19 + 24*x^18 + 59*x^17 + 46*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 126*x^8 + 70*x^7 + 56*x^6 + 126*x^5 + 116*x^4 + 53*x^3 + 120*x^2 + 61*x + 18, x^27 + 33*x^25 + 42*x^24 + 102*x^23 + 24*x^22 + 94*x^21 + 68*x^20 + 67*x^19 + 24*x^18 + 11*x^17 + 6*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 86*x^8 + 86*x^7 + 56*x^6 + 46*x^5 + 4*x^4 + 101*x^3 + 120*x^2 + 77*x + 58, x^27 + 33*x^25 + 26*x^24 + 54*x^23 + 40*x^22 + 46*x^21 + 52*x^20 + 115*x^19 + 8*x^18 + 59*x^17 + 6*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 70*x^8 + 102*x^7 + 8*x^6 + 62*x^5 + 52*x^4 + 85*x^3 + 40*x^2 + 61*x + 90, x^27 + 33*x^25 + 54*x^24 + 70*x^23 + 8*x^22 + 126*x^21 + 92*x^20 + 99*x^19 + 72*x^18 + 107*x^17 + 58*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 10*x^8 + 54*x^7 + 104*x^6 + 78*x^5 + 28*x^4 + 5*x^3 + 104*x^2 + 45*x + 70, x^27 + 33*x^25 + 10*x^24 + 54*x^23 + 40*x^22 + 110*x^21 + 20*x^20 + 115*x^19 + 8*x^18 + 123*x^17 + 22*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 86*x^8 + 102*x^7 + 8*x^6 + 126*x^5 + 20*x^4 + 85*x^3 + 40*x^2 + 125*x + 74, x^27 + 33*x^25 + 66*x^24 + 118*x^23 + 120*x^22 + 78*x^21 + 20*x^20 + 115*x^19 + 56*x^18 + 91*x^17 + 14*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 126*x^8 + 38*x^7 + 24*x^6 + 94*x^5 + 84*x^4 + 85*x^3 + 24*x^2 + 93*x + 114, x^27 + 33*x^25 + 98*x^24 + 6*x^23 + 72*x^22 + 94*x^21 + 100*x^20 + 99*x^19 + 104*x^18 + 75*x^17 + 94*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 62*x^8 + 118*x^7 + 40*x^6 + 46*x^5 + 100*x^4 + 5*x^3 + 8*x^2 + 13*x + 66, x^27 + 33*x^25 + 6*x^24 + 38*x^23 + 8*x^22 + 30*x^21 + 124*x^20 + 3*x^19 + 72*x^18 + 75*x^17 + 106*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 58*x^8 + 22*x^7 + 104*x^6 + 110*x^5 + 60*x^4 + 37*x^3 + 104*x^2 + 13*x + 22, x^27 + 33*x^25 + 82*x^24 + 22*x^23 + 88*x^22 + 46*x^21 + 20*x^20 + 83*x^19 + 88*x^18 + 123*x^17 + 30*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 46*x^8 + 70*x^7 + 120*x^6 + 62*x^5 + 84*x^4 + 53*x^3 + 56*x^2 + 125*x + 34, x^27 + 33*x^25 + 126*x^24 + 70*x^23 + 24*x^22 + 30*x^21 + 60*x^20 + 35*x^19 + 56*x^18 + 11*x^17 + 98*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 34*x^8 + 54*x^7 + 56*x^6 + 110*x^5 + 60*x^4 + 69*x^3 + 24*x^2 + 77*x + 62, x^27 + 33*x^25 + 98*x^24 + 70*x^23 + 104*x^22 + 30*x^21 + 4*x^20 + 35*x^19 + 72*x^18 + 11*x^17 + 62*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 126*x^8 + 54*x^7 + 72*x^6 + 110*x^5 + 4*x^4 + 69*x^3 + 104*x^2 + 77*x + 34, x^27 + 33*x^25 + 78*x^24 + 6*x^23 + 88*x^22 + 30*x^21 + 28*x^20 + 99*x^19 + 120*x^18 + 11*x^17 + 82*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 82*x^8 + 118*x^7 + 120*x^6 + 110*x^5 + 28*x^4 + 5*x^3 + 88*x^2 + 77*x + 78, x^27 + 33*x^25 + 50*x^24 + 102*x^23 + 72*x^22 + 126*x^21 + 4*x^20 + 3*x^19 + 104*x^18 + 43*x^17 + 14*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 110*x^8 + 86*x^7 + 40*x^6 + 78*x^5 + 4*x^4 + 37*x^3 + 8*x^2 + 109*x + 18, x^27 + 33*x^25 + 126*x^24 + 38*x^23 + 24*x^22 + 126*x^21 + 60*x^20 + 67*x^19 + 56*x^18 + 43*x^17 + 98*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 34*x^8 + 22*x^7 + 56*x^6 + 78*x^5 + 60*x^4 + 101*x^3 + 24*x^2 + 109*x + 62, x^27 + 33*x^25 + 102*x^24 + 70*x^23 + 104*x^22 + 62*x^21 + 28*x^20 + 99*x^19 + 104*x^18 + 43*x^17 + 42*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 26*x^8 + 54*x^7 + 72*x^6 + 14*x^5 + 92*x^4 + 5*x^3 + 8*x^2 + 109*x + 22, x^27 + 33*x^25 + 46*x^24 + 86*x^23 + 104*x^22 + 46*x^21 + 108*x^20 + 19*x^19 + 104*x^18 + 123*x^17 + 98*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 82*x^8 + 6*x^7 + 72*x^6 + 62*x^5 + 44*x^4 + 117*x^3 + 8*x^2 + 125*x + 94, x^27 + 33*x^25 + 98*x^24 + 86*x^23 + 24*x^22 + 110*x^21 + 52*x^20 + 19*x^19 + 24*x^18 + 59*x^17 + 14*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 30*x^8 + 6*x^7 + 56*x^6 + 126*x^5 + 116*x^4 + 117*x^3 + 120*x^2 + 61*x + 50, x^27 + 33*x^25 + 2*x^24 + 22*x^23 + 88*x^22 + 110*x^21 + 116*x^20 + 83*x^19 + 88*x^18 + 59*x^17 + 110*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 126*x^8 + 70*x^7 + 120*x^6 + 126*x^5 + 52*x^4 + 53*x^3 + 56*x^2 + 61*x + 82, x^27 + 33*x^25 + 30*x^24 + 6*x^23 + 24*x^22 + 94*x^21 + 124*x^20 + 99*x^19 + 56*x^18 + 75*x^17 + 66*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 2*x^8 + 118*x^7 + 56*x^6 + 46*x^5 + 124*x^4 + 5*x^3 + 24*x^2 + 13*x + 94, x^27 + 33*x^25 + 78*x^24 + 118*x^23 + 104*x^22 + 78*x^21 + 44*x^20 + 115*x^19 + 104*x^18 + 91*x^17 + 66*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 50*x^8 + 38*x^7 + 72*x^6 + 94*x^5 + 108*x^4 + 85*x^3 + 8*x^2 + 93*x + 126, x^27 + 33*x^25 + 38*x^24 + 22*x^23 + 88*x^22 + 14*x^21 + 76*x^20 + 19*x^19 + 120*x^18 + 91*x^17 + 58*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 122*x^8 + 70*x^7 + 120*x^6 + 30*x^5 + 76*x^4 + 117*x^3 + 88*x^2 + 93*x + 102, x^27 + 33*x^25 + 54*x^24 + 38*x^23 + 72*x^22 + 30*x^21 + 92*x^20 + 3*x^19 + 8*x^18 + 75*x^17 + 58*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 10*x^8 + 22*x^7 + 40*x^6 + 110*x^5 + 28*x^4 + 37*x^3 + 40*x^2 + 13*x + 70, x^27 + 33*x^25 + 42*x^24 + 102*x^23 + 88*x^22 + 94*x^21 + 4*x^20 + 67*x^19 + 88*x^18 + 11*x^17 + 70*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 86*x^8 + 86*x^7 + 120*x^6 + 46*x^5 + 68*x^4 + 101*x^3 + 56*x^2 + 77*x + 122, x^27 + 33*x^25 + 22*x^24 + 6*x^23 + 72*x^22 + 62*x^21 + 92*x^20 + 35*x^19 + 8*x^18 + 43*x^17 + 26*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 42*x^8 + 118*x^7 + 40*x^6 + 14*x^5 + 28*x^4 + 69*x^3 + 40*x^2 + 109*x + 102, x^27 + 33*x^25 + 22*x^24 + 102*x^23 + 40*x^22 + 94*x^21 + 124*x^20 + 67*x^19 + 40*x^18 + 11*x^17 + 122*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 106*x^8 + 86*x^7 + 8*x^6 + 46*x^5 + 60*x^4 + 101*x^3 + 72*x^2 + 77*x + 70, x^27 + 33*x^25 + 30*x^24 + 22*x^23 + 104*x^22 + 46*x^21 + 76*x^20 + 83*x^19 + 104*x^18 + 123*x^17 + 114*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 98*x^8 + 70*x^7 + 72*x^6 + 62*x^5 + 12*x^4 + 53*x^3 + 8*x^2 + 125*x + 78, x^27 + 33*x^25 + 78*x^24 + 6*x^23 + 120*x^22 + 94*x^21 + 124*x^20 + 99*x^19 + 88*x^18 + 75*x^17 + 114*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 18*x^8 + 118*x^7 + 24*x^6 + 46*x^5 + 124*x^4 + 5*x^3 + 56*x^2 + 13*x + 110, x^27 + 33*x^25 + 98*x^24 + 54*x^23 + 120*x^22 + 78*x^21 + 20*x^20 + 51*x^19 + 56*x^18 + 91*x^17 + 46*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 94*x^8 + 102*x^7 + 24*x^6 + 94*x^5 + 84*x^4 + 21*x^3 + 24*x^2 + 93*x + 82, x^27 + 33*x^25 + 110*x^24 + 6*x^23 + 120*x^22 + 94*x^21 + 60*x^20 + 99*x^19 + 88*x^18 + 75*x^17 + 82*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 114*x^8 + 118*x^7 + 24*x^6 + 46*x^5 + 60*x^4 + 5*x^3 + 56*x^2 + 13*x + 14, x^27 + 33*x^25 + 38*x^24 + 22*x^23 + 88*x^22 + 78*x^21 + 12*x^20 + 19*x^19 + 120*x^18 + 27*x^17 + 122*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 122*x^8 + 70*x^7 + 120*x^6 + 94*x^5 + 12*x^4 + 117*x^3 + 88*x^2 + 29*x + 38, x^27 + 33*x^25 + 86*x^24 + 54*x^23 + 120*x^22 + 110*x^21 + 76*x^20 + 115*x^19 + 88*x^18 + 123*x^17 + 106*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 10*x^8 + 102*x^7 + 24*x^6 + 126*x^5 + 76*x^4 + 85*x^3 + 56*x^2 + 125*x + 118, x^27 + 33*x^25 + 70*x^24 + 54*x^23 + 88*x^22 + 46*x^21 + 12*x^20 + 115*x^19 + 120*x^18 + 59*x^17 + 26*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 90*x^8 + 102*x^7 + 120*x^6 + 62*x^5 + 12*x^4 + 85*x^3 + 88*x^2 + 61*x + 6, x^27 + 33*x^25 + 118*x^24 + 70*x^23 + 40*x^22 + 126*x^21 + 124*x^20 + 99*x^19 + 40*x^18 + 107*x^17 + 90*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 10*x^8 + 54*x^7 + 8*x^6 + 78*x^5 + 60*x^4 + 5*x^3 + 72*x^2 + 45*x + 102, x^27 + 33*x^25 + 122*x^24 + 22*x^23 + 40*x^22 + 14*x^21 + 116*x^20 + 19*x^19 + 8*x^18 + 91*x^17 + 38*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 102*x^8 + 70*x^7 + 8*x^6 + 30*x^5 + 116*x^4 + 117*x^3 + 40*x^2 + 93*x + 58, x^27 + 33*x^25 + 74*x^24 + 86*x^23 + 8*x^22 + 14*x^21 + 116*x^20 + 83*x^19 + 40*x^18 + 91*x^17 + 118*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 86*x^8 + 6*x^7 + 104*x^6 + 30*x^5 + 116*x^4 + 53*x^3 + 72*x^2 + 93*x + 42, x^27 + 33*x^25 + 10*x^24 + 102*x^23 + 56*x^22 + 30*x^21 + 100*x^20 + 67*x^19 + 120*x^18 + 75*x^17 + 70*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 54*x^8 + 86*x^7 + 88*x^6 + 110*x^5 + 36*x^4 + 101*x^3 + 88*x^2 + 13*x + 58, x^27 + 33*x^25 + 94*x^24 + 54*x^23 + 104*x^22 + 14*x^21 + 12*x^20 + 51*x^19 + 104*x^18 + 27*x^17 + 114*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 34*x^8 + 102*x^7 + 72*x^6 + 30*x^5 + 76*x^4 + 21*x^3 + 8*x^2 + 29*x + 78, x^27 + 33*x^25 + 126*x^24 + 70*x^23 + 56*x^22 + 30*x^21 + 92*x^20 + 35*x^19 + 24*x^18 + 11*x^17 + 66*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 98*x^8 + 54*x^7 + 88*x^6 + 110*x^5 + 92*x^4 + 69*x^3 + 120*x^2 + 77*x + 30, x^27 + 33*x^25 + 82*x^24 + 102*x^23 + 72*x^22 + 126*x^21 + 68*x^20 + 3*x^19 + 104*x^18 + 43*x^17 + 110*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 78*x^8 + 86*x^7 + 40*x^6 + 78*x^5 + 68*x^4 + 37*x^3 + 8*x^2 + 109*x + 50, x^27 + 33*x^25 + 10*x^24 + 86*x^23 + 40*x^22 + 14*x^21 + 20*x^20 + 83*x^19 + 8*x^18 + 91*x^17 + 22*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 86*x^8 + 6*x^7 + 8*x^6 + 30*x^5 + 20*x^4 + 53*x^3 + 40*x^2 + 93*x + 74, x^27 + 33*x^25 + 54*x^24 + 86*x^23 + 56*x^22 + 14*x^21 + 76*x^20 + 83*x^19 + 24*x^18 + 91*x^17 + 74*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 42*x^8 + 6*x^7 + 88*x^6 + 30*x^5 + 76*x^4 + 53*x^3 + 120*x^2 + 93*x + 22, x^27 + 33*x^25 + 62*x^24 + 86*x^23 + 8*x^22 + 46*x^21 + 108*x^20 + 19*x^19 + 72*x^18 + 123*x^17 + 114*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 2*x^8 + 6*x^7 + 104*x^6 + 62*x^5 + 44*x^4 + 117*x^3 + 104*x^2 + 125*x + 14, x^27 + 33*x^25 + 34*x^24 + 70*x^23 + 40*x^22 + 94*x^21 + 4*x^20 + 35*x^19 + 8*x^18 + 75*x^17 + 126*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 62*x^8 + 54*x^7 + 8*x^6 + 46*x^5 + 4*x^4 + 69*x^3 + 40*x^2 + 13*x + 98, x^27 + 33*x^25 + 122*x^24 + 118*x^23 + 40*x^22 + 110*x^21 + 116*x^20 + 51*x^19 + 8*x^18 + 123*x^17 + 38*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 102*x^8 + 38*x^7 + 8*x^6 + 126*x^5 + 116*x^4 + 21*x^3 + 40*x^2 + 125*x + 58, x^27 + 33*x^25 + 6*x^24 + 38*x^23 + 8*x^22 + 94*x^21 + 60*x^20 + 3*x^19 + 72*x^18 + 11*x^17 + 42*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 58*x^8 + 22*x^7 + 104*x^6 + 46*x^5 + 124*x^4 + 37*x^3 + 104*x^2 + 77*x + 86, x^27 + 33*x^25 + 38*x^24 + 118*x^23 + 88*x^22 + 110*x^21 + 76*x^20 + 51*x^19 + 120*x^18 + 123*x^17 + 58*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 122*x^8 + 38*x^7 + 120*x^6 + 126*x^5 + 76*x^4 + 21*x^3 + 88*x^2 + 125*x + 102, x^27 + 33*x^25 + 62*x^24 + 86*x^23 + 104*x^22 + 46*x^21 + 76*x^20 + 19*x^19 + 104*x^18 + 123*x^17 + 18*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 66*x^8 + 6*x^7 + 72*x^6 + 62*x^5 + 12*x^4 + 117*x^3 + 8*x^2 + 125*x + 46, x^27 + 33*x^25 + 46*x^24 + 54*x^23 + 104*x^22 + 78*x^21 + 44*x^20 + 51*x^19 + 104*x^18 + 91*x^17 + 34*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 82*x^8 + 102*x^7 + 72*x^6 + 94*x^5 + 108*x^4 + 21*x^3 + 8*x^2 + 93*x + 30, x^27 + 33*x^25 + 74*x^24 + 54*x^23 + 72*x^22 + 110*x^21 + 52*x^20 + 115*x^19 + 104*x^18 + 123*x^17 + 54*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 86*x^8 + 102*x^7 + 40*x^6 + 126*x^5 + 52*x^4 + 85*x^3 + 8*x^2 + 125*x + 106, x^27 + 33*x^25 + 42*x^24 + 54*x^23 + 40*x^22 + 46*x^21 + 20*x^20 + 115*x^19 + 8*x^18 + 59*x^17 + 54*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 54*x^8 + 102*x^7 + 8*x^6 + 62*x^5 + 20*x^4 + 85*x^3 + 40*x^2 + 61*x + 42, x^27 + 33*x^25 + 82*x^24 + 102*x^23 + 8*x^22 + 126*x^21 + 4*x^20 + 3*x^19 + 40*x^18 + 43*x^17 + 46*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 78*x^8 + 86*x^7 + 104*x^6 + 78*x^5 + 4*x^4 + 37*x^3 + 72*x^2 + 109*x + 114, x^27 + 33*x^25 + 86*x^24 + 22*x^23 + 88*x^22 + 78*x^21 + 44*x^20 + 19*x^19 + 120*x^18 + 27*x^17 + 10*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 74*x^8 + 70*x^7 + 120*x^6 + 94*x^5 + 44*x^4 + 117*x^3 + 88*x^2 + 29*x + 22, x^27 + 33*x^25 + 50*x^24 + 118*x^23 + 120*x^22 + 78*x^21 + 52*x^20 + 115*x^19 + 56*x^18 + 91*x^17 + 94*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 14*x^8 + 38*x^7 + 24*x^6 + 94*x^5 + 116*x^4 + 85*x^3 + 24*x^2 + 93*x + 34, x^27 + 33*x^25 + 2*x^24 + 6*x^23 + 8*x^22 + 30*x^21 + 36*x^20 + 99*x^19 + 40*x^18 + 11*x^17 + 62*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 30*x^8 + 118*x^7 + 104*x^6 + 110*x^5 + 36*x^4 + 5*x^3 + 72*x^2 + 77*x + 98, x^27 + 33*x^25 + 74*x^24 + 118*x^23 + 104*x^22 + 110*x^21 + 20*x^20 + 51*x^19 + 72*x^18 + 123*x^17 + 86*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 22*x^8 + 38*x^7 + 72*x^6 + 126*x^5 + 20*x^4 + 21*x^3 + 104*x^2 + 125*x + 10, x^27 + 33*x^25 + 10*x^24 + 118*x^23 + 72*x^22 + 110*x^21 + 116*x^20 + 51*x^19 + 104*x^18 + 123*x^17 + 54*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 22*x^8 + 38*x^7 + 40*x^6 + 126*x^5 + 116*x^4 + 21*x^3 + 8*x^2 + 125*x + 106, x^27 + 33*x^25 + 18*x^24 + 70*x^23 + 104*x^22 + 94*x^21 + 100*x^20 + 35*x^19 + 72*x^18 + 75*x^17 + 14*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 78*x^8 + 54*x^7 + 72*x^6 + 46*x^5 + 100*x^4 + 69*x^3 + 104*x^2 + 13*x + 82, x^27 + 33*x^25 + 122*x^24 + 118*x^23 + 104*x^22 + 46*x^21 + 116*x^20 + 51*x^19 + 72*x^18 + 59*x^17 + 38*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 102*x^8 + 38*x^7 + 72*x^6 + 62*x^5 + 116*x^4 + 21*x^3 + 104*x^2 + 61*x + 58, x^27 + 33*x^25 + 102*x^24 + 6*x^23 + 104*x^22 + 62*x^21 + 92*x^20 + 35*x^19 + 104*x^18 + 43*x^17 + 106*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 26*x^8 + 118*x^7 + 72*x^6 + 14*x^5 + 28*x^4 + 69*x^3 + 8*x^2 + 109*x + 86, x^27 + 33*x^25 + 14*x^24 + 54*x^23 + 72*x^22 + 78*x^21 + 76*x^20 + 51*x^19 + 8*x^18 + 91*x^17 + 98*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 50*x^8 + 102*x^7 + 40*x^6 + 94*x^5 + 12*x^4 + 21*x^3 + 40*x^2 + 93*x + 30, x^27 + 33*x^25 + 98*x^24 + 54*x^23 + 88*x^22 + 14*x^21 + 52*x^20 + 51*x^19 + 88*x^18 + 27*x^17 + 14*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 30*x^8 + 102*x^7 + 120*x^6 + 30*x^5 + 116*x^4 + 21*x^3 + 56*x^2 + 29*x + 50, x^27 + 33*x^25 + 30*x^24 + 102*x^23 + 88*x^22 + 62*x^21 + 60*x^20 + 3*x^19 + 120*x^18 + 107*x^17 + 2*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 2*x^8 + 86*x^7 + 120*x^6 + 14*x^5 + 60*x^4 + 37*x^3 + 88*x^2 + 45*x + 30, x^27 + 33*x^25 + 62*x^24 + 102*x^23 + 56*x^22 + 126*x^21 + 28*x^20 + 3*x^19 + 24*x^18 + 43*x^17 + 66*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 34*x^8 + 86*x^7 + 88*x^6 + 78*x^5 + 28*x^4 + 37*x^3 + 120*x^2 + 109*x + 30, x^27 + 33*x^25 + 38*x^24 + 86*x^23 + 88*x^22 + 78*x^21 + 76*x^20 + 83*x^19 + 120*x^18 + 27*x^17 + 58*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 122*x^8 + 6*x^7 + 120*x^6 + 94*x^5 + 76*x^4 + 53*x^3 + 88*x^2 + 29*x + 102, x^27 + 33*x^25 + 34*x^24 + 86*x^23 + 24*x^22 + 46*x^21 + 116*x^20 + 19*x^19 + 24*x^18 + 123*x^17 + 14*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 94*x^8 + 6*x^7 + 56*x^6 + 62*x^5 + 52*x^4 + 117*x^3 + 120*x^2 + 125*x + 50, x^27 + 33*x^25 + 34*x^24 + 6*x^23 + 8*x^22 + 94*x^21 + 36*x^20 + 99*x^19 + 40*x^18 + 75*x^17 + 94*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 126*x^8 + 118*x^7 + 104*x^6 + 46*x^5 + 36*x^4 + 5*x^3 + 72*x^2 + 13*x + 66, x^27 + 33*x^25 + 6*x^24 + 70*x^23 + 40*x^22 + 126*x^21 + 92*x^20 + 99*x^19 + 40*x^18 + 107*x^17 + 10*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 122*x^8 + 54*x^7 + 8*x^6 + 78*x^5 + 28*x^4 + 5*x^3 + 72*x^2 + 45*x + 54, x^27 + 33*x^25 + 118*x^24 + 22*x^23 + 120*x^22 + 14*x^21 + 76*x^20 + 19*x^19 + 88*x^18 + 91*x^17 + 10*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 106*x^8 + 70*x^7 + 24*x^6 + 30*x^5 + 76*x^4 + 117*x^3 + 56*x^2 + 93*x + 86, x^27 + 33*x^25 + 66*x^24 + 86*x^23 + 120*x^22 + 46*x^21 + 20*x^20 + 19*x^19 + 56*x^18 + 123*x^17 + 14*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 126*x^8 + 6*x^7 + 24*x^6 + 62*x^5 + 84*x^4 + 117*x^3 + 24*x^2 + 125*x + 114, x^27 + 33*x^25 + 46*x^24 + 118*x^23 + 8*x^22 + 14*x^21 + 76*x^20 + 115*x^19 + 72*x^18 + 27*x^17 + 2*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 18*x^8 + 38*x^7 + 104*x^6 + 30*x^5 + 12*x^4 + 85*x^3 + 104*x^2 + 29*x + 126, x^27 + 33*x^25 + 46*x^24 + 70*x^23 + 120*x^22 + 94*x^21 + 124*x^20 + 35*x^19 + 88*x^18 + 75*x^17 + 82*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 50*x^8 + 54*x^7 + 24*x^6 + 46*x^5 + 124*x^4 + 69*x^3 + 56*x^2 + 13*x + 14, x^27 + 33*x^25 + 90*x^24 + 6*x^23 + 120*x^22 + 62*x^21 + 4*x^20 + 35*x^19 + 56*x^18 + 43*x^17 + 118*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 102*x^8 + 118*x^7 + 24*x^6 + 14*x^5 + 68*x^4 + 69*x^3 + 24*x^2 + 109*x + 10, x^27 + 33*x^25 + 74*x^24 + 86*x^23 + 104*x^22 + 78*x^21 + 20*x^20 + 83*x^19 + 72*x^18 + 27*x^17 + 86*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 22*x^8 + 6*x^7 + 72*x^6 + 94*x^5 + 20*x^4 + 53*x^3 + 104*x^2 + 29*x + 10, x^27 + 33*x^25 + 2*x^24 + 118*x^23 + 56*x^22 + 14*x^21 + 20*x^20 + 115*x^19 + 120*x^18 + 27*x^17 + 78*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 62*x^8 + 38*x^7 + 88*x^6 + 30*x^5 + 84*x^4 + 85*x^3 + 88*x^2 + 29*x + 50, x^27 + 33*x^25 + 18*x^24 + 86*x^23 + 120*x^22 + 110*x^21 + 52*x^20 + 19*x^19 + 56*x^18 + 59*x^17 + 62*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 46*x^8 + 6*x^7 + 24*x^6 + 126*x^5 + 116*x^4 + 117*x^3 + 24*x^2 + 61*x + 66, x^27 + 33*x^25 + 122*x^24 + 86*x^23 + 40*x^22 + 78*x^21 + 116*x^20 + 83*x^19 + 8*x^18 + 27*x^17 + 38*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 102*x^8 + 6*x^7 + 8*x^6 + 94*x^5 + 116*x^4 + 53*x^3 + 40*x^2 + 29*x + 58, x^27 + 33*x^25 + 66*x^24 + 70*x^23 + 72*x^22 + 94*x^21 + 100*x^20 + 35*x^19 + 104*x^18 + 75*x^17 + 62*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 94*x^8 + 54*x^7 + 40*x^6 + 46*x^5 + 100*x^4 + 69*x^3 + 8*x^2 + 13*x + 98, x^27 + 33*x^25 + 2*x^24 + 22*x^23 + 120*x^22 + 46*x^21 + 84*x^20 + 83*x^19 + 56*x^18 + 123*x^17 + 14*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 62*x^8 + 70*x^7 + 24*x^6 + 62*x^5 + 20*x^4 + 53*x^3 + 24*x^2 + 125*x + 114, x^27 + 33*x^25 + 114*x^24 + 118*x^23 + 120*x^22 + 78*x^21 + 52*x^20 + 115*x^19 + 56*x^18 + 91*x^17 + 30*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 78*x^8 + 38*x^7 + 24*x^6 + 94*x^5 + 116*x^4 + 85*x^3 + 24*x^2 + 93*x + 98, x^27 + 33*x^25 + 62*x^24 + 54*x^23 + 104*x^22 + 78*x^21 + 12*x^20 + 51*x^19 + 104*x^18 + 91*x^17 + 82*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 66*x^8 + 102*x^7 + 72*x^6 + 94*x^5 + 76*x^4 + 21*x^3 + 8*x^2 + 93*x + 110, x^27 + 33*x^25 + 18*x^24 + 54*x^23 + 24*x^22 + 78*x^21 + 84*x^20 + 51*x^19 + 24*x^18 + 91*x^17 + 30*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 110*x^8 + 102*x^7 + 56*x^6 + 94*x^5 + 20*x^4 + 21*x^3 + 120*x^2 + 93*x + 34, x^27 + 33*x^25 + 58*x^24 + 38*x^23 + 56*x^22 + 94*x^21 + 4*x^20 + 3*x^19 + 120*x^18 + 11*x^17 + 86*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 6*x^8 + 22*x^7 + 88*x^6 + 46*x^5 + 68*x^4 + 37*x^3 + 88*x^2 + 77*x + 42, x^27 + 33*x^25 + 82*x^24 + 118*x^23 + 56*x^22 + 14*x^21 + 116*x^20 + 115*x^19 + 120*x^18 + 27*x^17 + 62*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 110*x^8 + 38*x^7 + 88*x^6 + 30*x^5 + 52*x^4 + 85*x^3 + 88*x^2 + 29*x + 66, x^27 + 33*x^25 + 42*x^24 + 6*x^23 + 24*x^22 + 126*x^21 + 68*x^20 + 35*x^19 + 24*x^18 + 107*x^17 + 6*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 86*x^8 + 118*x^7 + 56*x^6 + 78*x^5 + 4*x^4 + 69*x^3 + 120*x^2 + 45*x + 58, x^27 + 33*x^25 + 70*x^24 + 54*x^23 + 56*x^22 + 110*x^21 + 44*x^20 + 115*x^19 + 24*x^18 + 123*x^17 + 122*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 26*x^8 + 102*x^7 + 88*x^6 + 126*x^5 + 44*x^4 + 85*x^3 + 120*x^2 + 125*x + 102, x^27 + 33*x^25 + 18*x^24 + 54*x^23 + 24*x^22 + 14*x^21 + 20*x^20 + 51*x^19 + 24*x^18 + 27*x^17 + 94*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 110*x^8 + 102*x^7 + 56*x^6 + 30*x^5 + 84*x^4 + 21*x^3 + 120*x^2 + 29*x + 98, x^27 + 33*x^25 + 46*x^24 + 6*x^23 + 120*x^22 + 94*x^21 + 60*x^20 + 99*x^19 + 88*x^18 + 75*x^17 + 18*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 50*x^8 + 118*x^7 + 24*x^6 + 46*x^5 + 60*x^4 + 5*x^3 + 56*x^2 + 13*x + 78, x^27 + 33*x^25 + 78*x^24 + 86*x^23 + 104*x^22 + 46*x^21 + 44*x^20 + 19*x^19 + 104*x^18 + 123*x^17 + 66*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 50*x^8 + 6*x^7 + 72*x^6 + 62*x^5 + 108*x^4 + 117*x^3 + 8*x^2 + 125*x + 126, x^27 + 33*x^25 + 114*x^24 + 70*x^23 + 8*x^22 + 30*x^21 + 4*x^20 + 35*x^19 + 40*x^18 + 11*x^17 + 78*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 46*x^8 + 54*x^7 + 104*x^6 + 110*x^5 + 4*x^4 + 69*x^3 + 72*x^2 + 77*x + 82, x^27 + 33*x^25 + 26*x^24 + 70*x^23 + 120*x^22 + 126*x^21 + 4*x^20 + 99*x^19 + 56*x^18 + 107*x^17 + 54*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 38*x^8 + 54*x^7 + 24*x^6 + 78*x^5 + 68*x^4 + 5*x^3 + 24*x^2 + 45*x + 74, x^27 + 33*x^25 + 102*x^24 + 22*x^23 + 120*x^22 + 78*x^21 + 44*x^20 + 19*x^19 + 88*x^18 + 27*x^17 + 26*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 122*x^8 + 70*x^7 + 24*x^6 + 94*x^5 + 44*x^4 + 117*x^3 + 56*x^2 + 29*x + 70, x^27 + 33*x^25 + 82*x^24 + 6*x^23 + 40*x^22 + 94*x^21 + 100*x^20 + 99*x^19 + 8*x^18 + 75*x^17 + 78*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 14*x^8 + 118*x^7 + 8*x^6 + 46*x^5 + 100*x^4 + 5*x^3 + 40*x^2 + 13*x + 18, x^27 + 33*x^25 + 42*x^24 + 86*x^23 + 8*x^22 + 14*x^21 + 52*x^20 + 83*x^19 + 40*x^18 + 91*x^17 + 22*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 118*x^8 + 6*x^7 + 104*x^6 + 30*x^5 + 52*x^4 + 53*x^3 + 72*x^2 + 93*x + 10, x^27 + 33*x^25 + 114*x^24 + 70*x^23 + 72*x^22 + 30*x^21 + 68*x^20 + 35*x^19 + 104*x^18 + 11*x^17 + 14*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 46*x^8 + 54*x^7 + 40*x^6 + 110*x^5 + 68*x^4 + 69*x^3 + 8*x^2 + 77*x + 18, x^27 + 33*x^25 + 34*x^24 + 118*x^23 + 56*x^22 + 78*x^21 + 20*x^20 + 115*x^19 + 120*x^18 + 91*x^17 + 110*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 30*x^8 + 38*x^7 + 88*x^6 + 94*x^5 + 84*x^4 + 85*x^3 + 88*x^2 + 93*x + 18, x^27 + 33*x^25 + 18*x^24 + 118*x^23 + 120*x^22 + 78*x^21 + 116*x^20 + 115*x^19 + 56*x^18 + 91*x^17 + 126*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 46*x^8 + 38*x^7 + 24*x^6 + 94*x^5 + 52*x^4 + 85*x^3 + 24*x^2 + 93*x + 2, x^27 + 33*x^25 + 98*x^24 + 6*x^23 + 72*x^22 + 30*x^21 + 36*x^20 + 99*x^19 + 104*x^18 + 11*x^17 + 30*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 62*x^8 + 118*x^7 + 40*x^6 + 110*x^5 + 36*x^4 + 5*x^3 + 8*x^2 + 77*x + 2, x^27 + 33*x^25 + 38*x^24 + 54*x^23 + 88*x^22 + 46*x^21 + 76*x^20 + 115*x^19 + 120*x^18 + 59*x^17 + 58*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 122*x^8 + 102*x^7 + 120*x^6 + 62*x^5 + 76*x^4 + 85*x^3 + 88*x^2 + 61*x + 102, x^27 + 33*x^25 + 58*x^24 + 102*x^23 + 24*x^22 + 30*x^21 + 100*x^20 + 67*x^19 + 24*x^18 + 75*x^17 + 118*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 70*x^8 + 86*x^7 + 56*x^6 + 110*x^5 + 36*x^4 + 101*x^3 + 120*x^2 + 13*x + 74, x^27 + 33*x^25 + 94*x^24 + 22*x^23 + 40*x^22 + 46*x^21 + 12*x^20 + 83*x^19 + 40*x^18 + 123*x^17 + 114*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 34*x^8 + 70*x^7 + 8*x^6 + 62*x^5 + 76*x^4 + 53*x^3 + 72*x^2 + 125*x + 78, x^27 + 33*x^25 + 62*x^24 + 102*x^23 + 24*x^22 + 62*x^21 + 60*x^20 + 3*x^19 + 56*x^18 + 107*x^17 + 34*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 98*x^8 + 86*x^7 + 56*x^6 + 14*x^5 + 60*x^4 + 37*x^3 + 24*x^2 + 45*x + 126, x^27 + 33*x^25 + 10*x^24 + 22*x^23 + 40*x^22 + 78*x^21 + 20*x^20 + 19*x^19 + 8*x^18 + 27*x^17 + 22*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 86*x^8 + 70*x^7 + 8*x^6 + 94*x^5 + 20*x^4 + 117*x^3 + 40*x^2 + 29*x + 74, x^27 + 33*x^25 + 38*x^24 + 70*x^23 + 40*x^22 + 126*x^21 + 28*x^20 + 99*x^19 + 40*x^18 + 107*x^17 + 106*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 90*x^8 + 54*x^7 + 8*x^6 + 78*x^5 + 92*x^4 + 5*x^3 + 72*x^2 + 45*x + 86, x^27 + 33*x^25 + 50*x^24 + 70*x^23 + 40*x^22 + 30*x^21 + 36*x^20 + 35*x^19 + 8*x^18 + 11*x^17 + 110*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 46*x^8 + 54*x^7 + 8*x^6 + 110*x^5 + 36*x^4 + 69*x^3 + 40*x^2 + 77*x + 114, x^27 + 33*x^25 + 126*x^24 + 102*x^23 + 24*x^22 + 126*x^21 + 124*x^20 + 3*x^19 + 56*x^18 + 43*x^17 + 34*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 34*x^8 + 86*x^7 + 56*x^6 + 78*x^5 + 124*x^4 + 37*x^3 + 24*x^2 + 109*x + 126, x^27 + 33*x^25 + 122*x^24 + 102*x^23 + 24*x^22 + 30*x^21 + 100*x^20 + 67*x^19 + 24*x^18 + 75*x^17 + 54*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 6*x^8 + 86*x^7 + 56*x^6 + 110*x^5 + 36*x^4 + 101*x^3 + 120*x^2 + 13*x + 10, x^27 + 33*x^25 + 118*x^24 + 6*x^23 + 72*x^22 + 126*x^21 + 92*x^20 + 35*x^19 + 8*x^18 + 107*x^17 + 122*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 74*x^8 + 118*x^7 + 40*x^6 + 78*x^5 + 28*x^4 + 69*x^3 + 40*x^2 + 45*x + 6, x^27 + 33*x^25 + 70*x^24 + 102*x^23 + 8*x^22 + 30*x^21 + 60*x^20 + 67*x^19 + 72*x^18 + 75*x^17 + 106*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 122*x^8 + 86*x^7 + 104*x^6 + 110*x^5 + 124*x^4 + 101*x^3 + 104*x^2 + 13*x + 22, x^27 + 33*x^25 + 94*x^24 + 70*x^23 + 56*x^22 + 30*x^21 + 28*x^20 + 35*x^19 + 24*x^18 + 11*x^17 + 98*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 2*x^8 + 54*x^7 + 88*x^6 + 110*x^5 + 28*x^4 + 69*x^3 + 120*x^2 + 77*x + 126, x^27 + 33*x^25 + 82*x^24 + 6*x^23 + 8*x^22 + 94*x^21 + 68*x^20 + 99*x^19 + 40*x^18 + 75*x^17 + 110*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 78*x^8 + 118*x^7 + 104*x^6 + 46*x^5 + 68*x^4 + 5*x^3 + 72*x^2 + 13*x + 50, x^27 + 33*x^25 + 14*x^24 + 70*x^23 + 56*x^22 + 30*x^21 + 60*x^20 + 35*x^19 + 24*x^18 + 11*x^17 + 114*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 82*x^8 + 54*x^7 + 88*x^6 + 110*x^5 + 60*x^4 + 69*x^3 + 120*x^2 + 77*x + 110, x^27 + 33*x^25 + 22*x^24 + 70*x^23 + 104*x^22 + 62*x^21 + 60*x^20 + 99*x^19 + 104*x^18 + 43*x^17 + 58*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 106*x^8 + 54*x^7 + 72*x^6 + 14*x^5 + 124*x^4 + 5*x^3 + 8*x^2 + 109*x + 6, x^27 + 33*x^25 + 50*x^24 + 86*x^23 + 120*x^22 + 46*x^21 + 52*x^20 + 19*x^19 + 56*x^18 + 123*x^17 + 94*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 14*x^8 + 6*x^7 + 24*x^6 + 62*x^5 + 116*x^4 + 117*x^3 + 24*x^2 + 125*x + 34, x^27 + 33*x^25 + 42*x^24 + 54*x^23 + 104*x^22 + 46*x^21 + 84*x^20 + 115*x^19 + 72*x^18 + 59*x^17 + 118*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 54*x^8 + 102*x^7 + 72*x^6 + 62*x^5 + 84*x^4 + 85*x^3 + 104*x^2 + 61*x + 106, x^27 + 33*x^25 + 26*x^24 + 22*x^23 + 8*x^22 + 78*x^21 + 84*x^20 + 19*x^19 + 40*x^18 + 27*x^17 + 102*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 6*x^8 + 70*x^7 + 104*x^6 + 94*x^5 + 84*x^4 + 117*x^3 + 72*x^2 + 29*x + 58, x^27 + 33*x^25 + 106*x^24 + 38*x^23 + 56*x^22 + 94*x^21 + 36*x^20 + 3*x^19 + 120*x^18 + 11*x^17 + 102*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 86*x^8 + 22*x^7 + 88*x^6 + 46*x^5 + 100*x^4 + 37*x^3 + 88*x^2 + 77*x + 26, x^27 + 33*x^25 + 70*x^24 + 22*x^23 + 24*x^22 + 14*x^21 + 76*x^20 + 19*x^19 + 56*x^18 + 91*x^17 + 90*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 90*x^8 + 70*x^7 + 56*x^6 + 30*x^5 + 76*x^4 + 117*x^3 + 24*x^2 + 93*x + 70, x^27 + 33*x^25 + 70*x^24 + 38*x^23 + 104*x^22 + 94*x^21 + 28*x^20 + 3*x^19 + 104*x^18 + 11*x^17 + 10*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 58*x^8 + 22*x^7 + 72*x^6 + 46*x^5 + 92*x^4 + 37*x^3 + 8*x^2 + 77*x + 54, x^27 + 33*x^25 + 98*x^24 + 38*x^23 + 72*x^22 + 126*x^21 + 100*x^20 + 67*x^19 + 104*x^18 + 43*x^17 + 94*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 62*x^8 + 22*x^7 + 40*x^6 + 78*x^5 + 100*x^4 + 101*x^3 + 8*x^2 + 109*x + 66, x^27 + 33*x^25 + 86*x^24 + 70*x^23 + 104*x^22 + 126*x^21 + 124*x^20 + 99*x^19 + 104*x^18 + 107*x^17 + 58*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 42*x^8 + 54*x^7 + 72*x^6 + 78*x^5 + 60*x^4 + 5*x^3 + 8*x^2 + 45*x + 6, x^27 + 33*x^25 + 58*x^24 + 102*x^23 + 88*x^22 + 94*x^21 + 100*x^20 + 67*x^19 + 88*x^18 + 11*x^17 + 118*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 70*x^8 + 86*x^7 + 120*x^6 + 46*x^5 + 36*x^4 + 101*x^3 + 56*x^2 + 77*x + 74, x^27 + 33*x^25 + 98*x^24 + 102*x^23 + 72*x^22 + 62*x^21 + 100*x^20 + 3*x^19 + 104*x^18 + 107*x^17 + 94*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 62*x^8 + 86*x^7 + 40*x^6 + 14*x^5 + 100*x^4 + 37*x^3 + 8*x^2 + 45*x + 66, x^27 + 33*x^25 + 70*x^24 + 118*x^23 + 24*x^22 + 46*x^21 + 12*x^20 + 51*x^19 + 56*x^18 + 59*x^17 + 26*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 90*x^8 + 38*x^7 + 56*x^6 + 62*x^5 + 12*x^4 + 21*x^3 + 24*x^2 + 61*x + 6, x^27 + 33*x^25 + 94*x^24 + 38*x^23 + 88*x^22 + 62*x^21 + 124*x^20 + 67*x^19 + 120*x^18 + 107*x^17 + 2*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 66*x^8 + 22*x^7 + 120*x^6 + 14*x^5 + 124*x^4 + 101*x^3 + 88*x^2 + 45*x + 30, x^27 + 33*x^25 + 10*x^24 + 118*x^23 + 104*x^22 + 110*x^21 + 20*x^20 + 51*x^19 + 72*x^18 + 123*x^17 + 22*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 86*x^8 + 38*x^7 + 72*x^6 + 126*x^5 + 20*x^4 + 21*x^3 + 104*x^2 + 125*x + 74, x^27 + 33*x^25 + 114*x^24 + 6*x^23 + 72*x^22 + 30*x^21 + 4*x^20 + 99*x^19 + 104*x^18 + 11*x^17 + 78*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 46*x^8 + 118*x^7 + 40*x^6 + 110*x^5 + 4*x^4 + 5*x^3 + 8*x^2 + 77*x + 82, x^27 + 33*x^25 + 18*x^24 + 6*x^23 + 104*x^22 + 94*x^21 + 36*x^20 + 99*x^19 + 72*x^18 + 75*x^17 + 78*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 78*x^8 + 118*x^7 + 72*x^6 + 46*x^5 + 36*x^4 + 5*x^3 + 104*x^2 + 13*x + 18, x^27 + 33*x^25 + 126*x^24 + 86*x^23 + 8*x^22 + 46*x^21 + 108*x^20 + 19*x^19 + 72*x^18 + 123*x^17 + 50*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 66*x^8 + 6*x^7 + 104*x^6 + 62*x^5 + 44*x^4 + 117*x^3 + 104*x^2 + 125*x + 78, x^27 + 33*x^25 + 62*x^24 + 86*x^23 + 104*x^22 + 110*x^21 + 12*x^20 + 19*x^19 + 104*x^18 + 59*x^17 + 82*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 66*x^8 + 6*x^7 + 72*x^6 + 126*x^5 + 76*x^4 + 117*x^3 + 8*x^2 + 61*x + 110, x^27 + 33*x^25 + 6*x^24 + 6*x^23 + 8*x^22 + 62*x^21 + 60*x^20 + 35*x^19 + 72*x^18 + 43*x^17 + 42*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 58*x^8 + 118*x^7 + 104*x^6 + 14*x^5 + 124*x^4 + 69*x^3 + 104*x^2 + 109*x + 86, x^27 + 33*x^25 + 58*x^24 + 6*x^23 + 24*x^22 + 62*x^21 + 100*x^20 + 35*x^19 + 24*x^18 + 43*x^17 + 118*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 70*x^8 + 118*x^7 + 56*x^6 + 14*x^5 + 36*x^4 + 69*x^3 + 120*x^2 + 109*x + 74, x^27 + 33*x^25 + 58*x^24 + 86*x^23 + 40*x^22 + 14*x^21 + 52*x^20 + 83*x^19 + 8*x^18 + 91*x^17 + 38*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 38*x^8 + 6*x^7 + 8*x^6 + 30*x^5 + 52*x^4 + 53*x^3 + 40*x^2 + 93*x + 58, x^27 + 33*x^25 + 86*x^24 + 54*x^23 + 88*x^22 + 110*x^21 + 44*x^20 + 115*x^19 + 120*x^18 + 123*x^17 + 10*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 74*x^8 + 102*x^7 + 120*x^6 + 126*x^5 + 44*x^4 + 85*x^3 + 88*x^2 + 125*x + 22, x^27 + 33*x^25 + 42*x^24 + 6*x^23 + 120*x^22 + 62*x^21 + 100*x^20 + 35*x^19 + 56*x^18 + 43*x^17 + 102*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 22*x^8 + 118*x^7 + 24*x^6 + 14*x^5 + 36*x^4 + 69*x^3 + 24*x^2 + 109*x + 26, x^27 + 33*x^25 + 70*x^24 + 38*x^23 + 72*x^22 + 94*x^21 + 124*x^20 + 3*x^19 + 8*x^18 + 11*x^17 + 42*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 122*x^8 + 22*x^7 + 40*x^6 + 46*x^5 + 60*x^4 + 37*x^3 + 40*x^2 + 77*x + 86, x^27 + 33*x^25 + 78*x^24 + 38*x^23 + 120*x^22 + 126*x^21 + 124*x^20 + 67*x^19 + 88*x^18 + 43*x^17 + 114*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 18*x^8 + 22*x^7 + 24*x^6 + 78*x^5 + 124*x^4 + 101*x^3 + 56*x^2 + 109*x + 110, x^27 + 33*x^25 + 62*x^24 + 22*x^23 + 8*x^22 + 46*x^21 + 44*x^20 + 83*x^19 + 72*x^18 + 123*x^17 + 50*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 2*x^8 + 70*x^7 + 104*x^6 + 62*x^5 + 108*x^4 + 53*x^3 + 104*x^2 + 125*x + 78, x^27 + 33*x^25 + 114*x^24 + 86*x^23 + 24*x^22 + 110*x^21 + 20*x^20 + 19*x^19 + 24*x^18 + 59*x^17 + 62*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 14*x^8 + 6*x^7 + 56*x^6 + 126*x^5 + 84*x^4 + 117*x^3 + 120*x^2 + 61*x + 2, x^27 + 33*x^25 + 126*x^24 + 22*x^23 + 40*x^22 + 46*x^21 + 76*x^20 + 83*x^19 + 40*x^18 + 123*x^17 + 82*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 2*x^8 + 70*x^7 + 8*x^6 + 62*x^5 + 12*x^4 + 53*x^3 + 72*x^2 + 125*x + 110, x^27 + 33*x^25 + 74*x^24 + 6*x^23 + 88*x^22 + 126*x^21 + 68*x^20 + 35*x^19 + 88*x^18 + 107*x^17 + 38*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 54*x^8 + 118*x^7 + 120*x^6 + 78*x^5 + 4*x^4 + 69*x^3 + 56*x^2 + 45*x + 26, x^27 + 33*x^25 + 110*x^24 + 38*x^23 + 120*x^22 + 126*x^21 + 60*x^20 + 67*x^19 + 88*x^18 + 43*x^17 + 82*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 114*x^8 + 22*x^7 + 24*x^6 + 78*x^5 + 60*x^4 + 101*x^3 + 56*x^2 + 109*x + 14, x^27 + 33*x^25 + 18*x^24 + 102*x^23 + 72*x^22 + 126*x^21 + 68*x^20 + 3*x^19 + 104*x^18 + 43*x^17 + 46*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 14*x^8 + 86*x^7 + 40*x^6 + 78*x^5 + 68*x^4 + 37*x^3 + 8*x^2 + 109*x + 114, x^27 + 33*x^25 + 82*x^24 + 6*x^23 + 40*x^22 + 30*x^21 + 36*x^20 + 99*x^19 + 8*x^18 + 11*x^17 + 14*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 14*x^8 + 118*x^7 + 8*x^6 + 110*x^5 + 36*x^4 + 5*x^3 + 40*x^2 + 77*x + 82, x^27 + 33*x^25 + 78*x^24 + 102*x^23 + 120*x^22 + 62*x^21 + 124*x^20 + 3*x^19 + 88*x^18 + 107*x^17 + 114*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 18*x^8 + 86*x^7 + 24*x^6 + 14*x^5 + 124*x^4 + 37*x^3 + 56*x^2 + 45*x + 110, x^27 + 33*x^25 + 110*x^24 + 102*x^23 + 120*x^22 + 62*x^21 + 60*x^20 + 3*x^19 + 88*x^18 + 107*x^17 + 82*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 114*x^8 + 86*x^7 + 24*x^6 + 14*x^5 + 60*x^4 + 37*x^3 + 56*x^2 + 45*x + 14, x^27 + 33*x^25 + 126*x^24 + 102*x^23 + 24*x^22 + 62*x^21 + 60*x^20 + 3*x^19 + 56*x^18 + 107*x^17 + 98*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 34*x^8 + 86*x^7 + 56*x^6 + 14*x^5 + 60*x^4 + 37*x^3 + 24*x^2 + 45*x + 62, x^27 + 33*x^25 + 110*x^24 + 102*x^23 + 24*x^22 + 126*x^21 + 28*x^20 + 3*x^19 + 56*x^18 + 43*x^17 + 114*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 50*x^8 + 86*x^7 + 56*x^6 + 78*x^5 + 28*x^4 + 37*x^3 + 24*x^2 + 109*x + 46, x^27 + 33*x^25 + 110*x^24 + 54*x^23 + 104*x^22 + 78*x^21 + 44*x^20 + 51*x^19 + 104*x^18 + 91*x^17 + 98*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 18*x^8 + 102*x^7 + 72*x^6 + 94*x^5 + 108*x^4 + 21*x^3 + 8*x^2 + 93*x + 94, x^27 + 33*x^25 + 34*x^24 + 22*x^23 + 88*x^22 + 110*x^21 + 52*x^20 + 83*x^19 + 88*x^18 + 59*x^17 + 78*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 94*x^8 + 70*x^7 + 120*x^6 + 126*x^5 + 116*x^4 + 53*x^3 + 56*x^2 + 61*x + 114, x^27 + 33*x^25 + 14*x^24 + 86*x^23 + 104*x^22 + 110*x^21 + 108*x^20 + 19*x^19 + 104*x^18 + 59*x^17 + 66*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 114*x^8 + 6*x^7 + 72*x^6 + 126*x^5 + 44*x^4 + 117*x^3 + 8*x^2 + 61*x + 126, x^27 + 33*x^25 + 122*x^24 + 70*x^23 + 56*x^22 + 126*x^21 + 4*x^20 + 99*x^19 + 120*x^18 + 107*x^17 + 22*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 70*x^8 + 54*x^7 + 88*x^6 + 78*x^5 + 68*x^4 + 5*x^3 + 88*x^2 + 45*x + 106, x^27 + 33*x^25 + 90*x^24 + 54*x^23 + 40*x^22 + 46*x^21 + 52*x^20 + 115*x^19 + 8*x^18 + 59*x^17 + 70*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 6*x^8 + 102*x^7 + 8*x^6 + 62*x^5 + 52*x^4 + 85*x^3 + 40*x^2 + 61*x + 26, x^27 + 33*x^25 + 78*x^24 + 54*x^23 + 72*x^22 + 78*x^21 + 76*x^20 + 51*x^19 + 8*x^18 + 91*x^17 + 34*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 114*x^8 + 102*x^7 + 40*x^6 + 94*x^5 + 12*x^4 + 21*x^3 + 40*x^2 + 93*x + 94, x^27 + 33*x^25 + 122*x^24 + 22*x^23 + 8*x^22 + 78*x^21 + 20*x^20 + 19*x^19 + 40*x^18 + 27*x^17 + 6*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 38*x^8 + 70*x^7 + 104*x^6 + 94*x^5 + 20*x^4 + 117*x^3 + 72*x^2 + 29*x + 26, x^27 + 33*x^25 + 38*x^24 + 6*x^23 + 40*x^22 + 62*x^21 + 28*x^20 + 35*x^19 + 40*x^18 + 43*x^17 + 106*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 90*x^8 + 118*x^7 + 8*x^6 + 14*x^5 + 92*x^4 + 69*x^3 + 72*x^2 + 109*x + 86, x^27 + 33*x^25 + 66*x^24 + 86*x^23 + 120*x^22 + 110*x^21 + 84*x^20 + 19*x^19 + 56*x^18 + 59*x^17 + 78*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 126*x^8 + 6*x^7 + 24*x^6 + 126*x^5 + 20*x^4 + 117*x^3 + 24*x^2 + 61*x + 50, x^27 + 33*x^25 + 70*x^24 + 38*x^23 + 72*x^22 + 30*x^21 + 60*x^20 + 3*x^19 + 8*x^18 + 75*x^17 + 106*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 122*x^8 + 22*x^7 + 40*x^6 + 110*x^5 + 124*x^4 + 37*x^3 + 40*x^2 + 13*x + 22, x^27 + 33*x^25 + 50*x^24 + 38*x^23 + 8*x^22 + 62*x^21 + 68*x^20 + 67*x^19 + 40*x^18 + 107*x^17 + 78*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 110*x^8 + 22*x^7 + 104*x^6 + 14*x^5 + 68*x^4 + 101*x^3 + 72*x^2 + 45*x + 82, x^27 + 33*x^25 + 94*x^24 + 22*x^23 + 72*x^22 + 110*x^21 + 108*x^20 + 83*x^19 + 8*x^18 + 59*x^17 + 18*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 98*x^8 + 70*x^7 + 40*x^6 + 126*x^5 + 44*x^4 + 53*x^3 + 40*x^2 + 61*x + 110, x^27 + 33*x^25 + 102*x^24 + 6*x^23 + 72*x^22 + 126*x^21 + 124*x^20 + 35*x^19 + 8*x^18 + 107*x^17 + 74*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 90*x^8 + 118*x^7 + 40*x^6 + 78*x^5 + 60*x^4 + 69*x^3 + 40*x^2 + 45*x + 54, x^27 + 33*x^25 + 110*x^24 + 70*x^23 + 120*x^22 + 94*x^21 + 124*x^20 + 35*x^19 + 88*x^18 + 75*x^17 + 18*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 114*x^8 + 54*x^7 + 24*x^6 + 46*x^5 + 124*x^4 + 69*x^3 + 56*x^2 + 13*x + 78, x^27 + 33*x^25 + 30*x^24 + 86*x^23 + 104*x^22 + 110*x^21 + 76*x^20 + 19*x^19 + 104*x^18 + 59*x^17 + 114*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 98*x^8 + 6*x^7 + 72*x^6 + 126*x^5 + 12*x^4 + 117*x^3 + 8*x^2 + 61*x + 78, x^27 + 33*x^25 + 110*x^24 + 70*x^23 + 88*x^22 + 30*x^21 + 28*x^20 + 35*x^19 + 120*x^18 + 11*x^17 + 114*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 50*x^8 + 54*x^7 + 120*x^6 + 110*x^5 + 28*x^4 + 69*x^3 + 88*x^2 + 77*x + 46, x^27 + 33*x^25 + 22*x^24 + 38*x^23 + 72*x^22 + 94*x^21 + 92*x^20 + 3*x^19 + 8*x^18 + 11*x^17 + 26*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 42*x^8 + 22*x^7 + 40*x^6 + 46*x^5 + 28*x^4 + 37*x^3 + 40*x^2 + 77*x + 102, x^27 + 33*x^25 + 126*x^24 + 102*x^23 + 56*x^22 + 126*x^21 + 28*x^20 + 3*x^19 + 24*x^18 + 43*x^17 + 2*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 98*x^8 + 86*x^7 + 88*x^6 + 78*x^5 + 28*x^4 + 37*x^3 + 120*x^2 + 109*x + 94, x^27 + 33*x^25 + 110*x^24 + 118*x^23 + 8*x^22 + 14*x^21 + 76*x^20 + 115*x^19 + 72*x^18 + 27*x^17 + 66*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 82*x^8 + 38*x^7 + 104*x^6 + 30*x^5 + 12*x^4 + 85*x^3 + 104*x^2 + 29*x + 62, x^27 + 33*x^25 + 70*x^24 + 86*x^23 + 24*x^22 + 78*x^21 + 76*x^20 + 83*x^19 + 56*x^18 + 27*x^17 + 90*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 90*x^8 + 6*x^7 + 56*x^6 + 94*x^5 + 76*x^4 + 53*x^3 + 24*x^2 + 29*x + 70, x^27 + 33*x^25 + 6*x^24 + 6*x^23 + 104*x^22 + 126*x^21 + 92*x^20 + 35*x^19 + 104*x^18 + 107*x^17 + 10*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 122*x^8 + 118*x^7 + 72*x^6 + 78*x^5 + 28*x^4 + 69*x^3 + 8*x^2 + 45*x + 54, x^27 + 33*x^25 + 82*x^24 + 86*x^23 + 24*x^22 + 110*x^21 + 84*x^20 + 19*x^19 + 24*x^18 + 59*x^17 + 94*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 46*x^8 + 6*x^7 + 56*x^6 + 126*x^5 + 20*x^4 + 117*x^3 + 120*x^2 + 61*x + 98, x^27 + 33*x^25 + 14*x^24 + 54*x^23 + 40*x^22 + 14*x^21 + 108*x^20 + 51*x^19 + 40*x^18 + 27*x^17 + 66*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 114*x^8 + 102*x^7 + 8*x^6 + 30*x^5 + 44*x^4 + 21*x^3 + 72*x^2 + 29*x + 126, x^27 + 33*x^25 + 10*x^24 + 54*x^23 + 72*x^22 + 110*x^21 + 52*x^20 + 115*x^19 + 104*x^18 + 123*x^17 + 118*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 22*x^8 + 102*x^7 + 40*x^6 + 126*x^5 + 52*x^4 + 85*x^3 + 8*x^2 + 125*x + 42, x^27 + 33*x^25 + 66*x^24 + 6*x^23 + 8*x^22 + 30*x^21 + 36*x^20 + 99*x^19 + 40*x^18 + 11*x^17 + 126*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 94*x^8 + 118*x^7 + 104*x^6 + 110*x^5 + 36*x^4 + 5*x^3 + 72*x^2 + 77*x + 34, x^27 + 33*x^25 + 34*x^24 + 6*x^23 + 72*x^22 + 30*x^21 + 36*x^20 + 99*x^19 + 104*x^18 + 11*x^17 + 94*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 126*x^8 + 118*x^7 + 40*x^6 + 110*x^5 + 36*x^4 + 5*x^3 + 8*x^2 + 77*x + 66, x^27 + 33*x^25 + 66*x^24 + 86*x^23 + 24*x^22 + 110*x^21 + 116*x^20 + 19*x^19 + 24*x^18 + 59*x^17 + 46*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 62*x^8 + 6*x^7 + 56*x^6 + 126*x^5 + 52*x^4 + 117*x^3 + 120*x^2 + 61*x + 18, x^27 + 33*x^25 + 38*x^24 + 38*x^23 + 72*x^22 + 94*x^21 + 60*x^20 + 3*x^19 + 8*x^18 + 11*x^17 + 74*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 26*x^8 + 22*x^7 + 40*x^6 + 46*x^5 + 124*x^4 + 37*x^3 + 40*x^2 + 77*x + 54, x^27 + 33*x^25 + 106*x^24 + 70*x^23 + 88*x^22 + 62*x^21 + 4*x^20 + 99*x^19 + 88*x^18 + 43*x^17 + 6*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 22*x^8 + 54*x^7 + 120*x^6 + 14*x^5 + 68*x^4 + 5*x^3 + 56*x^2 + 109*x + 58, x^27 + 33*x^25 + 14*x^24 + 38*x^23 + 56*x^22 + 62*x^21 + 124*x^20 + 67*x^19 + 24*x^18 + 107*x^17 + 50*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 82*x^8 + 22*x^7 + 88*x^6 + 14*x^5 + 124*x^4 + 101*x^3 + 120*x^2 + 45*x + 46, x^27 + 33*x^25 + 34*x^24 + 38*x^23 + 8*x^22 + 126*x^21 + 36*x^20 + 67*x^19 + 40*x^18 + 43*x^17 + 94*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 126*x^8 + 22*x^7 + 104*x^6 + 78*x^5 + 36*x^4 + 101*x^3 + 72*x^2 + 109*x + 66, x^27 + 33*x^25 + 62*x^24 + 38*x^23 + 120*x^22 + 126*x^21 + 28*x^20 + 67*x^19 + 88*x^18 + 43*x^17 + 66*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 34*x^8 + 22*x^7 + 24*x^6 + 78*x^5 + 28*x^4 + 101*x^3 + 56*x^2 + 109*x + 30, x^27 + 33*x^25 + 106*x^24 + 118*x^23 + 8*x^22 + 110*x^21 + 116*x^20 + 51*x^19 + 40*x^18 + 123*x^17 + 22*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 54*x^8 + 38*x^7 + 104*x^6 + 126*x^5 + 116*x^4 + 21*x^3 + 72*x^2 + 125*x + 10, x^27 + 33*x^25 + 42*x^24 + 54*x^23 + 72*x^22 + 110*x^21 + 116*x^20 + 115*x^19 + 104*x^18 + 123*x^17 + 86*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 118*x^8 + 102*x^7 + 40*x^6 + 126*x^5 + 116*x^4 + 85*x^3 + 8*x^2 + 125*x + 74, x^27 + 33*x^25 + 34*x^24 + 54*x^23 + 56*x^22 + 14*x^21 + 20*x^20 + 51*x^19 + 120*x^18 + 27*x^17 + 110*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 30*x^8 + 102*x^7 + 88*x^6 + 30*x^5 + 84*x^4 + 21*x^3 + 88*x^2 + 29*x + 18, x^27 + 33*x^25 + 98*x^24 + 38*x^23 + 104*x^22 + 62*x^21 + 68*x^20 + 67*x^19 + 72*x^18 + 107*x^17 + 126*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 126*x^8 + 22*x^7 + 72*x^6 + 14*x^5 + 68*x^4 + 101*x^3 + 104*x^2 + 45*x + 98, x^27 + 33*x^25 + 38*x^24 + 86*x^23 + 88*x^22 + 14*x^21 + 12*x^20 + 83*x^19 + 120*x^18 + 91*x^17 + 122*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 122*x^8 + 6*x^7 + 120*x^6 + 30*x^5 + 12*x^4 + 53*x^3 + 88*x^2 + 93*x + 38, x^27 + 33*x^25 + 98*x^24 + 22*x^23 + 120*x^22 + 110*x^21 + 84*x^20 + 83*x^19 + 56*x^18 + 59*x^17 + 110*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 94*x^8 + 70*x^7 + 24*x^6 + 126*x^5 + 20*x^4 + 53*x^3 + 24*x^2 + 61*x + 18, x^27 + 33*x^25 + 38*x^24 + 102*x^23 + 104*x^22 + 94*x^21 + 28*x^20 + 67*x^19 + 104*x^18 + 11*x^17 + 106*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 90*x^8 + 86*x^7 + 72*x^6 + 46*x^5 + 92*x^4 + 101*x^3 + 8*x^2 + 77*x + 86, x^27 + 33*x^25 + 14*x^24 + 54*x^23 + 8*x^22 + 14*x^21 + 76*x^20 + 51*x^19 + 72*x^18 + 27*x^17 + 98*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 50*x^8 + 102*x^7 + 104*x^6 + 30*x^5 + 12*x^4 + 21*x^3 + 104*x^2 + 29*x + 30, x^27 + 33*x^25 + 82*x^24 + 118*x^23 + 24*x^22 + 14*x^21 + 84*x^20 + 115*x^19 + 24*x^18 + 27*x^17 + 94*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 46*x^8 + 38*x^7 + 56*x^6 + 30*x^5 + 20*x^4 + 85*x^3 + 120*x^2 + 29*x + 98, x^27 + 33*x^25 + 26*x^24 + 86*x^23 + 40*x^22 + 14*x^21 + 116*x^20 + 83*x^19 + 8*x^18 + 91*x^17 + 70*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 70*x^8 + 6*x^7 + 8*x^6 + 30*x^5 + 116*x^4 + 53*x^3 + 40*x^2 + 93*x + 26, x^27 + 33*x^25 + 78*x^24 + 118*x^23 + 72*x^22 + 78*x^21 + 12*x^20 + 115*x^19 + 8*x^18 + 91*x^17 + 98*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 114*x^8 + 38*x^7 + 40*x^6 + 94*x^5 + 76*x^4 + 85*x^3 + 40*x^2 + 93*x + 30, x^27 + 33*x^25 + 74*x^24 + 38*x^23 + 88*x^22 + 94*x^21 + 4*x^20 + 3*x^19 + 88*x^18 + 11*x^17 + 102*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 54*x^8 + 22*x^7 + 120*x^6 + 46*x^5 + 68*x^4 + 37*x^3 + 56*x^2 + 77*x + 90, x^27 + 33*x^25 + 54*x^24 + 54*x^23 + 56*x^22 + 46*x^21 + 12*x^20 + 115*x^19 + 24*x^18 + 59*x^17 + 10*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 42*x^8 + 102*x^7 + 88*x^6 + 62*x^5 + 12*x^4 + 85*x^3 + 120*x^2 + 61*x + 86, x^27 + 33*x^25 + 78*x^24 + 6*x^23 + 24*x^22 + 30*x^21 + 92*x^20 + 99*x^19 + 56*x^18 + 11*x^17 + 18*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 82*x^8 + 118*x^7 + 56*x^6 + 110*x^5 + 92*x^4 + 5*x^3 + 24*x^2 + 77*x + 14, x^27 + 33*x^25 + 50*x^24 + 22*x^23 + 88*x^22 + 110*x^21 + 20*x^20 + 83*x^19 + 88*x^18 + 59*x^17 + 126*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 78*x^8 + 70*x^7 + 120*x^6 + 126*x^5 + 84*x^4 + 53*x^3 + 56*x^2 + 61*x + 66, x^27 + 33*x^25 + 46*x^24 + 6*x^23 + 24*x^22 + 94*x^21 + 92*x^20 + 99*x^19 + 56*x^18 + 75*x^17 + 114*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 114*x^8 + 118*x^7 + 56*x^6 + 46*x^5 + 92*x^4 + 5*x^3 + 24*x^2 + 13*x + 46, x^27 + 33*x^25 + 106*x^24 + 86*x^23 + 40*x^22 + 78*x^21 + 20*x^20 + 83*x^19 + 8*x^18 + 27*x^17 + 118*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 118*x^8 + 6*x^7 + 8*x^6 + 94*x^5 + 20*x^4 + 53*x^3 + 40*x^2 + 29*x + 106, x^27 + 33*x^25 + 86*x^24 + 70*x^23 + 104*x^22 + 62*x^21 + 60*x^20 + 99*x^19 + 104*x^18 + 43*x^17 + 122*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 42*x^8 + 54*x^7 + 72*x^6 + 14*x^5 + 124*x^4 + 5*x^3 + 8*x^2 + 109*x + 70, x^27 + 33*x^25 + 10*x^24 + 86*x^23 + 72*x^22 + 14*x^21 + 52*x^20 + 83*x^19 + 104*x^18 + 91*x^17 + 118*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 22*x^8 + 6*x^7 + 40*x^6 + 30*x^5 + 52*x^4 + 53*x^3 + 8*x^2 + 93*x + 42, x^27 + 33*x^25 + 82*x^24 + 38*x^23 + 40*x^22 + 126*x^21 + 100*x^20 + 67*x^19 + 8*x^18 + 43*x^17 + 78*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 14*x^8 + 22*x^7 + 8*x^6 + 78*x^5 + 100*x^4 + 101*x^3 + 40*x^2 + 109*x + 18, x^27 + 33*x^25 + 110*x^24 + 86*x^23 + 104*x^22 + 110*x^21 + 44*x^20 + 19*x^19 + 104*x^18 + 59*x^17 + 98*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 18*x^8 + 6*x^7 + 72*x^6 + 126*x^5 + 108*x^4 + 117*x^3 + 8*x^2 + 61*x + 94, x^27 + 33*x^25 + 118*x^24 + 102*x^23 + 72*x^22 + 94*x^21 + 92*x^20 + 67*x^19 + 8*x^18 + 11*x^17 + 122*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 74*x^8 + 86*x^7 + 40*x^6 + 46*x^5 + 28*x^4 + 101*x^3 + 40*x^2 + 77*x + 6, x^27 + 33*x^25 + 34*x^24 + 118*x^23 + 120*x^22 + 14*x^21 + 20*x^20 + 115*x^19 + 56*x^18 + 27*x^17 + 110*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 30*x^8 + 38*x^7 + 24*x^6 + 30*x^5 + 84*x^4 + 85*x^3 + 24*x^2 + 29*x + 18, x^27 + 33*x^25 + 22*x^24 + 38*x^23 + 40*x^22 + 30*x^21 + 124*x^20 + 3*x^19 + 40*x^18 + 75*x^17 + 122*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 106*x^8 + 22*x^7 + 8*x^6 + 110*x^5 + 60*x^4 + 37*x^3 + 72*x^2 + 13*x + 70, x^27 + 33*x^25 + 50*x^24 + 22*x^23 + 120*x^22 + 46*x^21 + 116*x^20 + 83*x^19 + 56*x^18 + 123*x^17 + 30*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 14*x^8 + 70*x^7 + 24*x^6 + 62*x^5 + 52*x^4 + 53*x^3 + 24*x^2 + 125*x + 98, x^27 + 33*x^25 + 122*x^24 + 54*x^23 + 8*x^22 + 46*x^21 + 84*x^20 + 115*x^19 + 40*x^18 + 59*x^17 + 70*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 38*x^8 + 102*x^7 + 104*x^6 + 62*x^5 + 84*x^4 + 85*x^3 + 72*x^2 + 61*x + 90, x^27 + 33*x^25 + 118*x^24 + 6*x^23 + 72*x^22 + 62*x^21 + 28*x^20 + 35*x^19 + 8*x^18 + 43*x^17 + 58*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 74*x^8 + 118*x^7 + 40*x^6 + 14*x^5 + 92*x^4 + 69*x^3 + 40*x^2 + 109*x + 70, x^27 + 33*x^25 + 30*x^24 + 70*x^23 + 88*x^22 + 94*x^21 + 124*x^20 + 35*x^19 + 120*x^18 + 75*x^17 + 66*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 2*x^8 + 54*x^7 + 120*x^6 + 46*x^5 + 124*x^4 + 69*x^3 + 88*x^2 + 13*x + 94, x^27 + 33*x^25 + 46*x^24 + 22*x^23 + 40*x^22 + 46*x^21 + 108*x^20 + 83*x^19 + 40*x^18 + 123*x^17 + 98*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 82*x^8 + 70*x^7 + 8*x^6 + 62*x^5 + 44*x^4 + 53*x^3 + 72*x^2 + 125*x + 94, x^27 + 33*x^25 + 118*x^24 + 102*x^23 + 8*x^22 + 30*x^21 + 92*x^20 + 67*x^19 + 72*x^18 + 75*x^17 + 122*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 74*x^8 + 86*x^7 + 104*x^6 + 110*x^5 + 28*x^4 + 101*x^3 + 104*x^2 + 13*x + 6, x^27 + 33*x^25 + 42*x^24 + 86*x^23 + 72*x^22 + 78*x^21 + 52*x^20 + 83*x^19 + 104*x^18 + 27*x^17 + 22*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 118*x^8 + 6*x^7 + 40*x^6 + 94*x^5 + 52*x^4 + 53*x^3 + 8*x^2 + 29*x + 10, x^27 + 33*x^25 + 22*x^24 + 22*x^23 + 88*x^22 + 78*x^21 + 44*x^20 + 19*x^19 + 120*x^18 + 27*x^17 + 74*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 10*x^8 + 70*x^7 + 120*x^6 + 94*x^5 + 44*x^4 + 117*x^3 + 88*x^2 + 29*x + 86, x^27 + 33*x^25 + 46*x^24 + 6*x^23 + 120*x^22 + 30*x^21 + 124*x^20 + 99*x^19 + 88*x^18 + 11*x^17 + 82*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 50*x^8 + 118*x^7 + 24*x^6 + 110*x^5 + 124*x^4 + 5*x^3 + 56*x^2 + 77*x + 14, x^27 + 33*x^25 + 50*x^24 + 70*x^23 + 72*x^22 + 30*x^21 + 68*x^20 + 35*x^19 + 104*x^18 + 11*x^17 + 78*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 110*x^8 + 54*x^7 + 40*x^6 + 110*x^5 + 68*x^4 + 69*x^3 + 8*x^2 + 77*x + 82, x^27 + 33*x^25 + 46*x^24 + 54*x^23 + 72*x^22 + 78*x^21 + 12*x^20 + 51*x^19 + 8*x^18 + 91*x^17 + 66*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 18*x^8 + 102*x^7 + 40*x^6 + 94*x^5 + 76*x^4 + 21*x^3 + 40*x^2 + 93*x + 62, x^27 + 33*x^25 + 106*x^24 + 70*x^23 + 56*x^22 + 126*x^21 + 36*x^20 + 99*x^19 + 120*x^18 + 107*x^17 + 102*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 86*x^8 + 54*x^7 + 88*x^6 + 78*x^5 + 100*x^4 + 5*x^3 + 88*x^2 + 45*x + 26, x^27 + 33*x^25 + 122*x^24 + 38*x^23 + 120*x^22 + 94*x^21 + 68*x^20 + 3*x^19 + 56*x^18 + 11*x^17 + 86*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 70*x^8 + 22*x^7 + 24*x^6 + 46*x^5 + 4*x^4 + 37*x^3 + 24*x^2 + 77*x + 42, x^27 + 33*x^25 + 30*x^24 + 22*x^23 + 8*x^22 + 110*x^21 + 44*x^20 + 83*x^19 + 72*x^18 + 59*x^17 + 18*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 34*x^8 + 70*x^7 + 104*x^6 + 126*x^5 + 108*x^4 + 53*x^3 + 104*x^2 + 61*x + 110, x^27 + 33*x^25 + 70*x^24 + 70*x^23 + 104*x^22 + 126*x^21 + 28*x^20 + 99*x^19 + 104*x^18 + 107*x^17 + 10*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 58*x^8 + 54*x^7 + 72*x^6 + 78*x^5 + 92*x^4 + 5*x^3 + 8*x^2 + 45*x + 54, x^27 + 33*x^25 + 50*x^24 + 6*x^23 + 104*x^22 + 94*x^21 + 100*x^20 + 99*x^19 + 72*x^18 + 75*x^17 + 46*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 46*x^8 + 118*x^7 + 72*x^6 + 46*x^5 + 100*x^4 + 5*x^3 + 104*x^2 + 13*x + 50, x^27 + 33*x^25 + 78*x^24 + 70*x^23 + 56*x^22 + 30*x^21 + 60*x^20 + 35*x^19 + 24*x^18 + 11*x^17 + 50*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 18*x^8 + 54*x^7 + 88*x^6 + 110*x^5 + 60*x^4 + 69*x^3 + 120*x^2 + 77*x + 46, x^27 + 33*x^25 + 118*x^24 + 38*x^23 + 8*x^22 + 30*x^21 + 28*x^20 + 3*x^19 + 72*x^18 + 75*x^17 + 58*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 74*x^8 + 22*x^7 + 104*x^6 + 110*x^5 + 92*x^4 + 37*x^3 + 104*x^2 + 13*x + 70, x^27 + 33*x^25 + 30*x^24 + 70*x^23 + 24*x^22 + 94*x^21 + 60*x^20 + 35*x^19 + 56*x^18 + 75*x^17 + 2*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 2*x^8 + 54*x^7 + 56*x^6 + 46*x^5 + 60*x^4 + 69*x^3 + 24*x^2 + 13*x + 30, x^27 + 33*x^25 + 22*x^24 + 86*x^23 + 88*x^22 + 14*x^21 + 44*x^20 + 83*x^19 + 120*x^18 + 91*x^17 + 74*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 10*x^8 + 6*x^7 + 120*x^6 + 30*x^5 + 44*x^4 + 53*x^3 + 88*x^2 + 93*x + 86, x^27 + 33*x^25 + 46*x^24 + 22*x^23 + 72*x^22 + 46*x^21 + 12*x^20 + 83*x^19 + 8*x^18 + 123*x^17 + 66*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 18*x^8 + 70*x^7 + 40*x^6 + 62*x^5 + 76*x^4 + 53*x^3 + 40*x^2 + 125*x + 62, x^27 + 33*x^25 + 46*x^24 + 70*x^23 + 56*x^22 + 94*x^21 + 60*x^20 + 35*x^19 + 24*x^18 + 75*x^17 + 18*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 50*x^8 + 54*x^7 + 88*x^6 + 46*x^5 + 60*x^4 + 69*x^3 + 120*x^2 + 13*x + 78, x^27 + 33*x^25 + 118*x^24 + 102*x^23 + 104*x^22 + 30*x^21 + 60*x^20 + 67*x^19 + 104*x^18 + 75*x^17 + 26*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 10*x^8 + 86*x^7 + 72*x^6 + 110*x^5 + 124*x^4 + 101*x^3 + 8*x^2 + 13*x + 38, x^27 + 33*x^25 + 42*x^24 + 6*x^23 + 56*x^22 + 126*x^21 + 100*x^20 + 35*x^19 + 120*x^18 + 107*x^17 + 102*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 22*x^8 + 118*x^7 + 88*x^6 + 78*x^5 + 36*x^4 + 69*x^3 + 88*x^2 + 45*x + 26, x^27 + 33*x^25 + 18*x^24 + 22*x^23 + 88*x^22 + 110*x^21 + 84*x^20 + 83*x^19 + 88*x^18 + 59*x^17 + 30*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 110*x^8 + 70*x^7 + 120*x^6 + 126*x^5 + 20*x^4 + 53*x^3 + 56*x^2 + 61*x + 34, x^27 + 33*x^25 + 74*x^24 + 70*x^23 + 88*x^22 + 62*x^21 + 68*x^20 + 99*x^19 + 88*x^18 + 43*x^17 + 38*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 54*x^8 + 54*x^7 + 120*x^6 + 14*x^5 + 4*x^4 + 5*x^3 + 56*x^2 + 109*x + 26, x^27 + 33*x^25 + 126*x^24 + 54*x^23 + 8*x^22 + 78*x^21 + 44*x^20 + 51*x^19 + 72*x^18 + 91*x^17 + 114*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 66*x^8 + 102*x^7 + 104*x^6 + 94*x^5 + 108*x^4 + 21*x^3 + 104*x^2 + 93*x + 14, x^27 + 33*x^25 + 118*x^24 + 22*x^23 + 24*x^22 + 78*x^21 + 44*x^20 + 19*x^19 + 56*x^18 + 27*x^17 + 42*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 42*x^8 + 70*x^7 + 56*x^6 + 94*x^5 + 44*x^4 + 117*x^3 + 24*x^2 + 29*x + 118, x^27 + 33*x^25 + 42*x^24 + 6*x^23 + 88*x^22 + 126*x^21 + 4*x^20 + 35*x^19 + 88*x^18 + 107*x^17 + 70*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 86*x^8 + 118*x^7 + 120*x^6 + 78*x^5 + 68*x^4 + 69*x^3 + 56*x^2 + 45*x + 122, x^27 + 33*x^25 + 54*x^24 + 118*x^23 + 120*x^22 + 110*x^21 + 76*x^20 + 51*x^19 + 88*x^18 + 123*x^17 + 74*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 42*x^8 + 38*x^7 + 24*x^6 + 126*x^5 + 76*x^4 + 21*x^3 + 56*x^2 + 125*x + 22, x^27 + 33*x^25 + 114*x^24 + 22*x^23 + 24*x^22 + 110*x^21 + 84*x^20 + 83*x^19 + 24*x^18 + 59*x^17 + 126*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 14*x^8 + 70*x^7 + 56*x^6 + 126*x^5 + 20*x^4 + 53*x^3 + 120*x^2 + 61*x + 66, x^27 + 33*x^25 + 106*x^24 + 102*x^23 + 24*x^22 + 30*x^21 + 4*x^20 + 67*x^19 + 24*x^18 + 75*x^17 + 6*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 22*x^8 + 86*x^7 + 56*x^6 + 110*x^5 + 68*x^4 + 101*x^3 + 120*x^2 + 13*x + 58, x^27 + 33*x^25 + 42*x^24 + 70*x^23 + 24*x^22 + 62*x^21 + 68*x^20 + 99*x^19 + 24*x^18 + 43*x^17 + 6*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 86*x^8 + 54*x^7 + 56*x^6 + 14*x^5 + 4*x^4 + 5*x^3 + 120*x^2 + 109*x + 58, x^27 + 33*x^25 + 74*x^24 + 118*x^23 + 8*x^22 + 110*x^21 + 52*x^20 + 51*x^19 + 40*x^18 + 123*x^17 + 54*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 86*x^8 + 38*x^7 + 104*x^6 + 126*x^5 + 52*x^4 + 21*x^3 + 72*x^2 + 125*x + 106, x^27 + 33*x^25 + 34*x^24 + 6*x^23 + 40*x^22 + 94*x^21 + 68*x^20 + 99*x^19 + 8*x^18 + 75*x^17 + 62*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 62*x^8 + 118*x^7 + 8*x^6 + 46*x^5 + 68*x^4 + 5*x^3 + 40*x^2 + 13*x + 34, x^27 + 33*x^25 + 106*x^24 + 54*x^23 + 104*x^22 + 110*x^21 + 20*x^20 + 115*x^19 + 72*x^18 + 123*x^17 + 118*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 118*x^8 + 102*x^7 + 72*x^6 + 126*x^5 + 20*x^4 + 85*x^3 + 104*x^2 + 125*x + 106, x^27 + 33*x^25 + 58*x^24 + 22*x^23 + 8*x^22 + 78*x^21 + 20*x^20 + 19*x^19 + 40*x^18 + 27*x^17 + 70*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 102*x^8 + 70*x^7 + 104*x^6 + 94*x^5 + 20*x^4 + 117*x^3 + 72*x^2 + 29*x + 90, x^27 + 33*x^25 + 110*x^24 + 70*x^23 + 56*x^22 + 30*x^21 + 124*x^20 + 35*x^19 + 24*x^18 + 11*x^17 + 18*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 114*x^8 + 54*x^7 + 88*x^6 + 110*x^5 + 124*x^4 + 69*x^3 + 120*x^2 + 77*x + 78, x^27 + 33*x^25 + 66*x^24 + 6*x^23 + 40*x^22 + 30*x^21 + 68*x^20 + 99*x^19 + 8*x^18 + 11*x^17 + 94*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 30*x^8 + 118*x^7 + 8*x^6 + 110*x^5 + 68*x^4 + 5*x^3 + 40*x^2 + 77*x + 2, x^27 + 33*x^25 + 14*x^24 + 22*x^23 + 104*x^22 + 46*x^21 + 108*x^20 + 83*x^19 + 104*x^18 + 123*x^17 + 66*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 114*x^8 + 70*x^7 + 72*x^6 + 62*x^5 + 44*x^4 + 53*x^3 + 8*x^2 + 125*x + 126, x^27 + 33*x^25 + 18*x^24 + 70*x^23 + 40*x^22 + 94*x^21 + 36*x^20 + 35*x^19 + 8*x^18 + 75*x^17 + 78*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 78*x^8 + 54*x^7 + 8*x^6 + 46*x^5 + 36*x^4 + 69*x^3 + 40*x^2 + 13*x + 18, x^27 + 33*x^25 + 38*x^24 + 22*x^23 + 56*x^22 + 14*x^21 + 44*x^20 + 19*x^19 + 24*x^18 + 91*x^17 + 90*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 58*x^8 + 70*x^7 + 88*x^6 + 30*x^5 + 44*x^4 + 117*x^3 + 120*x^2 + 93*x + 6, x^27 + 33*x^25 + 98*x^24 + 38*x^23 + 72*x^22 + 62*x^21 + 36*x^20 + 67*x^19 + 104*x^18 + 107*x^17 + 30*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 62*x^8 + 22*x^7 + 40*x^6 + 14*x^5 + 36*x^4 + 101*x^3 + 8*x^2 + 45*x + 2, x^27 + 33*x^25 + 90*x^24 + 22*x^23 + 40*x^22 + 78*x^21 + 116*x^20 + 19*x^19 + 8*x^18 + 27*x^17 + 6*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 6*x^8 + 70*x^7 + 8*x^6 + 94*x^5 + 116*x^4 + 117*x^3 + 40*x^2 + 29*x + 90, x^27 + 33*x^25 + 122*x^24 + 6*x^23 + 88*x^22 + 62*x^21 + 36*x^20 + 35*x^19 + 88*x^18 + 43*x^17 + 118*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 6*x^8 + 118*x^7 + 120*x^6 + 14*x^5 + 100*x^4 + 69*x^3 + 56*x^2 + 109*x + 74, x^27 + 33*x^25 + 2*x^24 + 38*x^23 + 40*x^22 + 62*x^21 + 68*x^20 + 67*x^19 + 8*x^18 + 107*x^17 + 30*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 94*x^8 + 22*x^7 + 8*x^6 + 14*x^5 + 68*x^4 + 101*x^3 + 40*x^2 + 45*x + 66, x^27 + 33*x^25 + 14*x^24 + 70*x^23 + 88*x^22 + 30*x^21 + 92*x^20 + 35*x^19 + 120*x^18 + 11*x^17 + 82*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 8*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 18*x^8 + 54*x^7 + 120*x^6 + 110*x^5 + 92*x^4 + 69*x^3 + 88*x^2 + 77*x + 78, x^27 + 33*x^25 + 102*x^24 + 6*x^23 + 72*x^22 + 62*x^21 + 60*x^20 + 35*x^19 + 8*x^18 + 43*x^17 + 10*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 90*x^8 + 118*x^7 + 40*x^6 + 14*x^5 + 124*x^4 + 69*x^3 + 40*x^2 + 109*x + 118, x^27 + 33*x^25 + 58*x^24 + 70*x^23 + 56*x^22 + 62*x^21 + 68*x^20 + 99*x^19 + 120*x^18 + 43*x^17 + 22*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 6*x^8 + 54*x^7 + 88*x^6 + 14*x^5 + 4*x^4 + 5*x^3 + 88*x^2 + 109*x + 106, x^27 + 33*x^25 + 50*x^24 + 38*x^23 + 104*x^22 + 126*x^21 + 100*x^20 + 67*x^19 + 72*x^18 + 43*x^17 + 46*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 46*x^8 + 22*x^7 + 72*x^6 + 78*x^5 + 100*x^4 + 101*x^3 + 104*x^2 + 109*x + 50, x^27 + 33*x^25 + 54*x^24 + 86*x^23 + 88*x^22 + 14*x^21 + 108*x^20 + 83*x^19 + 120*x^18 + 91*x^17 + 42*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 106*x^8 + 6*x^7 + 120*x^6 + 30*x^5 + 108*x^4 + 53*x^3 + 88*x^2 + 93*x + 118, x^27 + 33*x^25 + 54*x^24 + 6*x^23 + 40*x^22 + 126*x^21 + 60*x^20 + 35*x^19 + 40*x^18 + 107*x^17 + 90*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 74*x^8 + 118*x^7 + 8*x^6 + 78*x^5 + 124*x^4 + 69*x^3 + 72*x^2 + 45*x + 102, x^27 + 33*x^25 + 50*x^24 + 102*x^23 + 104*x^22 + 62*x^21 + 100*x^20 + 3*x^19 + 72*x^18 + 107*x^17 + 46*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 46*x^8 + 86*x^7 + 72*x^6 + 14*x^5 + 100*x^4 + 37*x^3 + 104*x^2 + 45*x + 50, x^27 + 33*x^25 + 102*x^24 + 22*x^23 + 24*x^22 + 14*x^21 + 12*x^20 + 19*x^19 + 56*x^18 + 91*x^17 + 58*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 58*x^8 + 70*x^7 + 56*x^6 + 30*x^5 + 12*x^4 + 117*x^3 + 24*x^2 + 93*x + 102, x^27 + 33*x^25 + 42*x^24 + 118*x^23 + 8*x^22 + 110*x^21 + 116*x^20 + 51*x^19 + 40*x^18 + 123*x^17 + 86*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 118*x^8 + 38*x^7 + 104*x^6 + 126*x^5 + 116*x^4 + 21*x^3 + 72*x^2 + 125*x + 74, x^27 + 33*x^25 + 22*x^24 + 70*x^23 + 40*x^22 + 62*x^21 + 124*x^20 + 99*x^19 + 40*x^18 + 43*x^17 + 122*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 106*x^8 + 54*x^7 + 8*x^6 + 14*x^5 + 60*x^4 + 5*x^3 + 72*x^2 + 109*x + 70, x^27 + 33*x^25 + 14*x^24 + 54*x^23 + 104*x^22 + 14*x^21 + 44*x^20 + 51*x^19 + 104*x^18 + 27*x^17 + 2*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 114*x^8 + 102*x^7 + 72*x^6 + 30*x^5 + 108*x^4 + 21*x^3 + 8*x^2 + 29*x + 62, x^27 + 33*x^25 + 66*x^24 + 118*x^23 + 88*x^22 + 78*x^21 + 116*x^20 + 115*x^19 + 88*x^18 + 91*x^17 + 46*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 62*x^8 + 38*x^7 + 120*x^6 + 94*x^5 + 52*x^4 + 85*x^3 + 56*x^2 + 93*x + 18, x^27 + 33*x^25 + 118*x^24 + 6*x^23 + 40*x^22 + 126*x^21 + 60*x^20 + 35*x^19 + 40*x^18 + 107*x^17 + 26*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 10*x^8 + 118*x^7 + 8*x^6 + 78*x^5 + 124*x^4 + 69*x^3 + 72*x^2 + 45*x + 38, x^27 + 33*x^25 + 102*x^24 + 38*x^23 + 8*x^22 + 30*x^21 + 60*x^20 + 3*x^19 + 72*x^18 + 75*x^17 + 10*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 90*x^8 + 22*x^7 + 104*x^6 + 110*x^5 + 124*x^4 + 37*x^3 + 104*x^2 + 13*x + 118, x^27 + 33*x^25 + 38*x^24 + 118*x^23 + 56*x^22 + 110*x^21 + 44*x^20 + 51*x^19 + 24*x^18 + 123*x^17 + 90*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 58*x^8 + 38*x^7 + 88*x^6 + 126*x^5 + 44*x^4 + 21*x^3 + 120*x^2 + 125*x + 6, x^27 + 33*x^25 + 86*x^24 + 86*x^23 + 120*x^22 + 14*x^21 + 76*x^20 + 83*x^19 + 88*x^18 + 91*x^17 + 106*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 10*x^8 + 6*x^7 + 24*x^6 + 30*x^5 + 76*x^4 + 53*x^3 + 56*x^2 + 93*x + 118, x^27 + 33*x^25 + 70*x^24 + 38*x^23 + 40*x^22 + 94*x^21 + 92*x^20 + 3*x^19 + 40*x^18 + 11*x^17 + 74*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 58*x^8 + 22*x^7 + 8*x^6 + 46*x^5 + 28*x^4 + 37*x^3 + 72*x^2 + 77*x + 118, x^27 + 33*x^25 + 54*x^24 + 86*x^23 + 24*x^22 + 14*x^21 + 44*x^20 + 83*x^19 + 56*x^18 + 91*x^17 + 106*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 106*x^8 + 6*x^7 + 56*x^6 + 30*x^5 + 44*x^4 + 53*x^3 + 24*x^2 + 93*x + 54, x^27 + 33*x^25 + 58*x^24 + 22*x^23 + 104*x^22 + 14*x^21 + 52*x^20 + 19*x^19 + 72*x^18 + 91*x^17 + 38*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 38*x^8 + 70*x^7 + 72*x^6 + 30*x^5 + 52*x^4 + 117*x^3 + 104*x^2 + 93*x + 58, x^27 + 33*x^25 + 38*x^24 + 70*x^23 + 72*x^22 + 126*x^21 + 60*x^20 + 99*x^19 + 8*x^18 + 107*x^17 + 74*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 26*x^8 + 54*x^7 + 40*x^6 + 78*x^5 + 124*x^4 + 5*x^3 + 40*x^2 + 45*x + 54, x^27 + 33*x^25 + 14*x^24 + 22*x^23 + 8*x^22 + 46*x^21 + 12*x^20 + 83*x^19 + 72*x^18 + 123*x^17 + 34*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 50*x^8 + 70*x^7 + 104*x^6 + 62*x^5 + 76*x^4 + 53*x^3 + 104*x^2 + 125*x + 94, x^27 + 33*x^25 + 78*x^24 + 38*x^23 + 120*x^22 + 62*x^21 + 60*x^20 + 67*x^19 + 88*x^18 + 107*x^17 + 50*x^16 + 100*x^15 + 112*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 112*x^10 + 39*x^9 + 18*x^8 + 22*x^7 + 24*x^6 + 14*x^5 + 60*x^4 + 101*x^3 + 56*x^2 + 45*x + 46, x^27 + 33*x^25 + 6*x^24 + 38*x^23 + 104*x^22 + 94*x^21 + 28*x^20 + 3*x^19 + 104*x^18 + 11*x^17 + 74*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 122*x^8 + 22*x^7 + 72*x^6 + 46*x^5 + 92*x^4 + 37*x^3 + 8*x^2 + 77*x + 118, x^27 + 33*x^25 + 102*x^24 + 118*x^23 + 88*x^22 + 46*x^21 + 12*x^20 + 51*x^19 + 120*x^18 + 59*x^17 + 58*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 58*x^8 + 38*x^7 + 120*x^6 + 62*x^5 + 12*x^4 + 21*x^3 + 88*x^2 + 61*x + 102, x^27 + 33*x^25 + 126*x^24 + 22*x^23 + 72*x^22 + 110*x^21 + 44*x^20 + 83*x^19 + 8*x^18 + 59*x^17 + 114*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 66*x^8 + 70*x^7 + 40*x^6 + 126*x^5 + 108*x^4 + 53*x^3 + 40*x^2 + 61*x + 14, x^27 + 33*x^25 + 70*x^24 + 54*x^23 + 88*x^22 + 110*x^21 + 76*x^20 + 115*x^19 + 120*x^18 + 123*x^17 + 90*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 90*x^8 + 102*x^7 + 120*x^6 + 126*x^5 + 76*x^4 + 85*x^3 + 88*x^2 + 125*x + 70, x^27 + 33*x^25 + 14*x^24 + 118*x^23 + 104*x^22 + 14*x^21 + 108*x^20 + 115*x^19 + 104*x^18 + 27*x^17 + 66*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 114*x^8 + 38*x^7 + 72*x^6 + 30*x^5 + 44*x^4 + 85*x^3 + 8*x^2 + 29*x + 126, x^27 + 33*x^25 + 34*x^24 + 102*x^23 + 40*x^22 + 126*x^21 + 4*x^20 + 3*x^19 + 8*x^18 + 43*x^17 + 126*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 62*x^8 + 86*x^7 + 8*x^6 + 78*x^5 + 4*x^4 + 37*x^3 + 40*x^2 + 109*x + 98, x^27 + 33*x^25 + 74*x^24 + 86*x^23 + 72*x^22 + 14*x^21 + 52*x^20 + 83*x^19 + 104*x^18 + 91*x^17 + 54*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 86*x^8 + 6*x^7 + 40*x^6 + 30*x^5 + 52*x^4 + 53*x^3 + 8*x^2 + 93*x + 106, x^27 + 33*x^25 + 114*x^24 + 22*x^23 + 56*x^22 + 46*x^21 + 52*x^20 + 83*x^19 + 120*x^18 + 123*x^17 + 30*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 78*x^8 + 70*x^7 + 88*x^6 + 62*x^5 + 116*x^4 + 53*x^3 + 88*x^2 + 125*x + 98, x^27 + 33*x^25 + 74*x^24 + 118*x^23 + 72*x^22 + 46*x^21 + 52*x^20 + 51*x^19 + 104*x^18 + 59*x^17 + 54*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 86*x^8 + 38*x^7 + 40*x^6 + 62*x^5 + 52*x^4 + 21*x^3 + 8*x^2 + 61*x + 106, x^27 + 33*x^25 + 126*x^24 + 22*x^23 + 104*x^22 + 46*x^21 + 12*x^20 + 83*x^19 + 104*x^18 + 123*x^17 + 18*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 2*x^8 + 70*x^7 + 72*x^6 + 62*x^5 + 76*x^4 + 53*x^3 + 8*x^2 + 125*x + 46, x^27 + 33*x^25 + 106*x^24 + 102*x^23 + 24*x^22 + 94*x^21 + 68*x^20 + 67*x^19 + 24*x^18 + 11*x^17 + 70*x^16 + 100*x^15 + 48*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 112*x^10 + 103*x^9 + 22*x^8 + 86*x^7 + 56*x^6 + 46*x^5 + 4*x^4 + 101*x^3 + 120*x^2 + 77*x + 122, x^27 + 33*x^25 + 74*x^24 + 70*x^23 + 88*x^22 + 126*x^21 + 4*x^20 + 99*x^19 + 88*x^18 + 107*x^17 + 102*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 54*x^8 + 54*x^7 + 120*x^6 + 78*x^5 + 68*x^4 + 5*x^3 + 56*x^2 + 45*x + 90, x^27 + 33*x^25 + 2*x^24 + 22*x^23 + 88*x^22 + 46*x^21 + 52*x^20 + 83*x^19 + 88*x^18 + 123*x^17 + 46*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 126*x^8 + 70*x^7 + 120*x^6 + 62*x^5 + 116*x^4 + 53*x^3 + 56*x^2 + 125*x + 18, x^27 + 33*x^25 + 34*x^24 + 70*x^23 + 104*x^22 + 30*x^21 + 4*x^20 + 35*x^19 + 72*x^18 + 11*x^17 + 126*x^16 + 36*x^15 + 80*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 80*x^10 + 103*x^9 + 62*x^8 + 54*x^7 + 72*x^6 + 110*x^5 + 4*x^4 + 69*x^3 + 104*x^2 + 77*x + 98, x^27 + 33*x^25 + 78*x^24 + 118*x^23 + 40*x^22 + 78*x^21 + 108*x^20 + 115*x^19 + 40*x^18 + 91*x^17 + 2*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 50*x^8 + 38*x^7 + 8*x^6 + 94*x^5 + 44*x^4 + 85*x^3 + 72*x^2 + 93*x + 62, x^27 + 33*x^25 + 62*x^24 + 22*x^23 + 8*x^22 + 110*x^21 + 108*x^20 + 83*x^19 + 72*x^18 + 59*x^17 + 114*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 2*x^8 + 70*x^7 + 104*x^6 + 126*x^5 + 44*x^4 + 53*x^3 + 104*x^2 + 61*x + 14, x^27 + 33*x^25 + 114*x^24 + 22*x^23 + 120*x^22 + 110*x^21 + 52*x^20 + 83*x^19 + 56*x^18 + 59*x^17 + 30*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 78*x^8 + 70*x^7 + 24*x^6 + 126*x^5 + 116*x^4 + 53*x^3 + 24*x^2 + 61*x + 98, x^27 + 33*x^25 + 90*x^24 + 70*x^23 + 120*x^22 + 62*x^21 + 68*x^20 + 99*x^19 + 56*x^18 + 43*x^17 + 54*x^16 + 36*x^15 + 112*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 48*x^10 + 39*x^9 + 102*x^8 + 54*x^7 + 24*x^6 + 14*x^5 + 4*x^4 + 5*x^3 + 24*x^2 + 109*x + 74, x^27 + 33*x^25 + 102*x^24 + 86*x^23 + 24*x^22 + 78*x^21 + 12*x^20 + 83*x^19 + 56*x^18 + 27*x^17 + 58*x^16 + 68*x^15 + 48*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 48*x^10 + 7*x^9 + 58*x^8 + 6*x^7 + 56*x^6 + 94*x^5 + 12*x^4 + 53*x^3 + 24*x^2 + 29*x + 102, x^27 + 33*x^25 + 22*x^24 + 118*x^23 + 120*x^22 + 110*x^21 + 12*x^20 + 51*x^19 + 88*x^18 + 123*x^17 + 106*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 74*x^8 + 38*x^7 + 24*x^6 + 126*x^5 + 12*x^4 + 21*x^3 + 56*x^2 + 125*x + 118, x^27 + 33*x^25 + 106*x^24 + 54*x^23 + 8*x^22 + 46*x^21 + 116*x^20 + 115*x^19 + 40*x^18 + 59*x^17 + 22*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 54*x^8 + 102*x^7 + 104*x^6 + 62*x^5 + 116*x^4 + 85*x^3 + 72*x^2 + 61*x + 10, x^27 + 33*x^25 + 46*x^24 + 38*x^23 + 24*x^22 + 126*x^21 + 92*x^20 + 67*x^19 + 56*x^18 + 43*x^17 + 114*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 114*x^8 + 22*x^7 + 56*x^6 + 78*x^5 + 92*x^4 + 101*x^3 + 24*x^2 + 109*x + 46, x^27 + 33*x^25 + 70*x^24 + 6*x^23 + 104*x^22 + 126*x^21 + 92*x^20 + 35*x^19 + 104*x^18 + 107*x^17 + 74*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 58*x^8 + 118*x^7 + 72*x^6 + 78*x^5 + 28*x^4 + 69*x^3 + 8*x^2 + 45*x + 118, x^27 + 33*x^25 + 58*x^24 + 70*x^23 + 88*x^22 + 62*x^21 + 100*x^20 + 99*x^19 + 88*x^18 + 43*x^17 + 118*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 70*x^8 + 54*x^7 + 120*x^6 + 14*x^5 + 36*x^4 + 5*x^3 + 56*x^2 + 109*x + 74, x^27 + 33*x^25 + 22*x^24 + 102*x^23 + 8*x^22 + 30*x^21 + 28*x^20 + 67*x^19 + 72*x^18 + 75*x^17 + 90*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 42*x^8 + 86*x^7 + 104*x^6 + 110*x^5 + 92*x^4 + 101*x^3 + 104*x^2 + 13*x + 38, x^27 + 33*x^25 + 2*x^24 + 38*x^23 + 72*x^22 + 62*x^21 + 100*x^20 + 67*x^19 + 104*x^18 + 107*x^17 + 126*x^16 + 100*x^15 + 16*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 16*x^10 + 39*x^9 + 30*x^8 + 22*x^7 + 40*x^6 + 14*x^5 + 100*x^4 + 101*x^3 + 8*x^2 + 45*x + 34, x^27 + 33*x^25 + 46*x^24 + 102*x^23 + 24*x^22 + 62*x^21 + 92*x^20 + 3*x^19 + 56*x^18 + 107*x^17 + 114*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 114*x^8 + 86*x^7 + 56*x^6 + 14*x^5 + 92*x^4 + 37*x^3 + 24*x^2 + 45*x + 46, x^27 + 33*x^25 + 58*x^24 + 102*x^23 + 120*x^22 + 30*x^21 + 68*x^20 + 67*x^19 + 56*x^18 + 75*x^17 + 22*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 120*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 6*x^8 + 86*x^7 + 24*x^6 + 110*x^5 + 4*x^4 + 101*x^3 + 24*x^2 + 13*x + 106, x^27 + 33*x^25 + 110*x^24 + 54*x^23 + 72*x^22 + 78*x^21 + 12*x^20 + 51*x^19 + 8*x^18 + 91*x^17 + 2*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 82*x^8 + 102*x^7 + 40*x^6 + 94*x^5 + 76*x^4 + 21*x^3 + 40*x^2 + 93*x + 126, x^27 + 33*x^25 + 106*x^24 + 22*x^23 + 8*x^22 + 78*x^21 + 52*x^20 + 19*x^19 + 40*x^18 + 27*x^17 + 86*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 54*x^8 + 70*x^7 + 104*x^6 + 94*x^5 + 52*x^4 + 117*x^3 + 72*x^2 + 29*x + 74, x^27 + 33*x^25 + 10*x^24 + 102*x^23 + 120*x^22 + 30*x^21 + 36*x^20 + 67*x^19 + 56*x^18 + 75*x^17 + 6*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 54*x^8 + 86*x^7 + 24*x^6 + 110*x^5 + 100*x^4 + 101*x^3 + 24*x^2 + 13*x + 122, x^27 + 33*x^25 + 6*x^24 + 6*x^23 + 40*x^22 + 126*x^21 + 28*x^20 + 35*x^19 + 40*x^18 + 107*x^17 + 74*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 122*x^8 + 118*x^7 + 8*x^6 + 78*x^5 + 92*x^4 + 69*x^3 + 72*x^2 + 45*x + 118, x^27 + 33*x^25 + 46*x^24 + 118*x^23 + 104*x^22 + 14*x^21 + 44*x^20 + 115*x^19 + 104*x^18 + 27*x^17 + 34*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 40*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 82*x^8 + 38*x^7 + 72*x^6 + 30*x^5 + 108*x^4 + 85*x^3 + 8*x^2 + 29*x + 30, x^27 + 33*x^25 + 34*x^24 + 22*x^23 + 24*x^22 + 110*x^21 + 116*x^20 + 83*x^19 + 24*x^18 + 59*x^17 + 14*x^16 + 68*x^15 + 48*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 112*x^10 + 71*x^9 + 94*x^8 + 70*x^7 + 56*x^6 + 126*x^5 + 52*x^4 + 53*x^3 + 120*x^2 + 61*x + 50, x^27 + 33*x^25 + 58*x^24 + 118*x^23 + 40*x^22 + 110*x^21 + 116*x^20 + 51*x^19 + 8*x^18 + 123*x^17 + 102*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 38*x^8 + 38*x^7 + 8*x^6 + 126*x^5 + 116*x^4 + 21*x^3 + 40*x^2 + 125*x + 122, x^27 + 33*x^25 + 110*x^24 + 54*x^23 + 8*x^22 + 14*x^21 + 12*x^20 + 51*x^19 + 72*x^18 + 27*x^17 + 2*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 82*x^8 + 102*x^7 + 104*x^6 + 30*x^5 + 76*x^4 + 21*x^3 + 104*x^2 + 29*x + 126, x^27 + 33*x^25 + 30*x^24 + 102*x^23 + 24*x^22 + 126*x^21 + 60*x^20 + 3*x^19 + 56*x^18 + 43*x^17 + 2*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 72*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 2*x^8 + 86*x^7 + 56*x^6 + 78*x^5 + 60*x^4 + 37*x^3 + 24*x^2 + 109*x + 30, x^27 + 33*x^25 + 46*x^24 + 102*x^23 + 88*x^22 + 62*x^21 + 28*x^20 + 3*x^19 + 120*x^18 + 107*x^17 + 50*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 114*x^8 + 86*x^7 + 120*x^6 + 14*x^5 + 28*x^4 + 37*x^3 + 88*x^2 + 45*x + 110, x^27 + 33*x^25 + 70*x^24 + 86*x^23 + 56*x^22 + 14*x^21 + 44*x^20 + 83*x^19 + 24*x^18 + 91*x^17 + 122*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 26*x^8 + 6*x^7 + 88*x^6 + 30*x^5 + 44*x^4 + 53*x^3 + 120*x^2 + 93*x + 102, x^27 + 33*x^25 + 66*x^24 + 22*x^23 + 120*x^22 + 110*x^21 + 20*x^20 + 83*x^19 + 56*x^18 + 59*x^17 + 14*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 88*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 126*x^8 + 70*x^7 + 24*x^6 + 126*x^5 + 84*x^4 + 53*x^3 + 24*x^2 + 61*x + 114, x^27 + 33*x^25 + 94*x^24 + 6*x^23 + 24*x^22 + 30*x^21 + 60*x^20 + 99*x^19 + 56*x^18 + 11*x^17 + 66*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 66*x^8 + 118*x^7 + 56*x^6 + 110*x^5 + 60*x^4 + 5*x^3 + 24*x^2 + 77*x + 94, x^27 + 33*x^25 + 38*x^24 + 70*x^23 + 72*x^22 + 62*x^21 + 124*x^20 + 99*x^19 + 8*x^18 + 43*x^17 + 10*x^16 + 36*x^15 + 16*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 80*x^10 + 39*x^9 + 26*x^8 + 54*x^7 + 40*x^6 + 14*x^5 + 60*x^4 + 5*x^3 + 40*x^2 + 109*x + 118, x^27 + 33*x^25 + 122*x^24 + 22*x^23 + 104*x^22 + 78*x^21 + 116*x^20 + 19*x^19 + 72*x^18 + 27*x^17 + 38*x^16 + 68*x^15 + 80*x^14 + 116*x^13 + 88*x^12 + 87*x^11 + 80*x^10 + 7*x^9 + 102*x^8 + 70*x^7 + 72*x^6 + 94*x^5 + 116*x^4 + 117*x^3 + 104*x^2 + 29*x + 58, x^27 + 33*x^25 + 98*x^24 + 70*x^23 + 72*x^22 + 94*x^21 + 36*x^20 + 35*x^19 + 104*x^18 + 75*x^17 + 30*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 120*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 62*x^8 + 54*x^7 + 40*x^6 + 46*x^5 + 36*x^4 + 69*x^3 + 8*x^2 + 13*x + 2, x^27 + 33*x^25 + 90*x^24 + 6*x^23 + 88*x^22 + 126*x^21 + 36*x^20 + 35*x^19 + 88*x^18 + 107*x^17 + 86*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 38*x^8 + 118*x^7 + 120*x^6 + 78*x^5 + 100*x^4 + 69*x^3 + 56*x^2 + 45*x + 106, x^27 + 33*x^25 + 102*x^24 + 118*x^23 + 120*x^22 + 110*x^21 + 108*x^20 + 51*x^19 + 88*x^18 + 123*x^17 + 90*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 122*x^8 + 38*x^7 + 24*x^6 + 126*x^5 + 108*x^4 + 21*x^3 + 56*x^2 + 125*x + 6, x^27 + 33*x^25 + 54*x^24 + 70*x^23 + 40*x^22 + 62*x^21 + 60*x^20 + 99*x^19 + 40*x^18 + 43*x^17 + 90*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 74*x^8 + 54*x^7 + 8*x^6 + 14*x^5 + 124*x^4 + 5*x^3 + 72*x^2 + 109*x + 102, x^27 + 33*x^25 + 118*x^24 + 38*x^23 + 104*x^22 + 94*x^21 + 60*x^20 + 3*x^19 + 104*x^18 + 11*x^17 + 26*x^16 + 100*x^15 + 80*x^14 + 20*x^13 + 8*x^12 + 55*x^11 + 16*x^10 + 103*x^9 + 10*x^8 + 22*x^7 + 72*x^6 + 46*x^5 + 124*x^4 + 37*x^3 + 8*x^2 + 77*x + 38, x^27 + 33*x^25 + 54*x^24 + 102*x^23 + 8*x^22 + 30*x^21 + 92*x^20 + 67*x^19 + 72*x^18 + 75*x^17 + 58*x^16 + 100*x^15 + 16*x^14 + 20*x^13 + 72*x^12 + 55*x^11 + 80*x^10 + 103*x^9 + 10*x^8 + 86*x^7 + 104*x^6 + 110*x^5 + 28*x^4 + 101*x^3 + 104*x^2 + 13*x + 70, x^27 + 33*x^25 + 106*x^24 + 38*x^23 + 56*x^22 + 30*x^21 + 100*x^20 + 3*x^19 + 120*x^18 + 75*x^17 + 38*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 86*x^8 + 22*x^7 + 88*x^6 + 110*x^5 + 36*x^4 + 37*x^3 + 88*x^2 + 13*x + 90, x^27 + 33*x^25 + 10*x^24 + 102*x^23 + 120*x^22 + 94*x^21 + 100*x^20 + 67*x^19 + 56*x^18 + 11*x^17 + 70*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 54*x^8 + 86*x^7 + 24*x^6 + 46*x^5 + 36*x^4 + 101*x^3 + 24*x^2 + 77*x + 58, x^27 + 33*x^25 + 38*x^24 + 118*x^23 + 24*x^22 + 46*x^21 + 76*x^20 + 51*x^19 + 56*x^18 + 59*x^17 + 58*x^16 + 4*x^15 + 48*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 48*x^10 + 71*x^9 + 122*x^8 + 38*x^7 + 56*x^6 + 62*x^5 + 76*x^4 + 21*x^3 + 24*x^2 + 61*x + 102, x^27 + 33*x^25 + 42*x^24 + 118*x^23 + 104*x^22 + 46*x^21 + 20*x^20 + 51*x^19 + 72*x^18 + 59*x^17 + 54*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 54*x^8 + 38*x^7 + 72*x^6 + 62*x^5 + 20*x^4 + 21*x^3 + 104*x^2 + 61*x + 42, x^27 + 33*x^25 + 106*x^24 + 6*x^23 + 24*x^22 + 126*x^21 + 68*x^20 + 35*x^19 + 24*x^18 + 107*x^17 + 70*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 120*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 22*x^8 + 118*x^7 + 56*x^6 + 78*x^5 + 4*x^4 + 69*x^3 + 120*x^2 + 45*x + 122, x^27 + 33*x^25 + 14*x^24 + 102*x^23 + 24*x^22 + 126*x^21 + 92*x^20 + 3*x^19 + 56*x^18 + 43*x^17 + 82*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 18*x^8 + 86*x^7 + 56*x^6 + 78*x^5 + 92*x^4 + 37*x^3 + 24*x^2 + 109*x + 78, x^27 + 33*x^25 + 14*x^24 + 86*x^23 + 40*x^22 + 46*x^21 + 108*x^20 + 19*x^19 + 40*x^18 + 123*x^17 + 66*x^16 + 68*x^15 + 80*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 16*x^10 + 71*x^9 + 114*x^8 + 6*x^7 + 8*x^6 + 62*x^5 + 44*x^4 + 117*x^3 + 72*x^2 + 125*x + 126, x^27 + 33*x^25 + 62*x^24 + 118*x^23 + 104*x^22 + 78*x^21 + 76*x^20 + 115*x^19 + 104*x^18 + 91*x^17 + 18*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 66*x^8 + 38*x^7 + 72*x^6 + 94*x^5 + 12*x^4 + 85*x^3 + 8*x^2 + 93*x + 46, x^27 + 33*x^25 + 106*x^24 + 38*x^23 + 120*x^22 + 94*x^21 + 100*x^20 + 3*x^19 + 56*x^18 + 11*x^17 + 38*x^16 + 100*x^15 + 112*x^14 + 20*x^13 + 56*x^12 + 55*x^11 + 48*x^10 + 103*x^9 + 86*x^8 + 22*x^7 + 24*x^6 + 46*x^5 + 36*x^4 + 37*x^3 + 24*x^2 + 77*x + 90, x^27 + 33*x^25 + 86*x^24 + 54*x^23 + 120*x^22 + 46*x^21 + 12*x^20 + 115*x^19 + 88*x^18 + 59*x^17 + 42*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 40*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 10*x^8 + 102*x^7 + 24*x^6 + 62*x^5 + 12*x^4 + 85*x^3 + 56*x^2 + 61*x + 54, x^27 + 33*x^25 + 6*x^24 + 54*x^23 + 56*x^22 + 110*x^21 + 44*x^20 + 115*x^19 + 24*x^18 + 123*x^17 + 58*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 90*x^8 + 102*x^7 + 88*x^6 + 126*x^5 + 44*x^4 + 85*x^3 + 120*x^2 + 125*x + 38, x^27 + 33*x^25 + 106*x^24 + 54*x^23 + 40*x^22 + 46*x^21 + 20*x^20 + 115*x^19 + 8*x^18 + 59*x^17 + 118*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 118*x^8 + 102*x^7 + 8*x^6 + 62*x^5 + 20*x^4 + 85*x^3 + 40*x^2 + 61*x + 106, x^27 + 33*x^25 + 102*x^24 + 86*x^23 + 120*x^22 + 78*x^21 + 108*x^20 + 83*x^19 + 88*x^18 + 27*x^17 + 90*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 104*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 122*x^8 + 6*x^7 + 24*x^6 + 94*x^5 + 108*x^4 + 53*x^3 + 56*x^2 + 29*x + 6, x^27 + 33*x^25 + 62*x^24 + 118*x^23 + 40*x^22 + 78*x^21 + 12*x^20 + 115*x^19 + 40*x^18 + 91*x^17 + 82*x^16 + 4*x^15 + 80*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 16*x^10 + 7*x^9 + 66*x^8 + 38*x^7 + 8*x^6 + 94*x^5 + 76*x^4 + 85*x^3 + 72*x^2 + 93*x + 110, x^27 + 33*x^25 + 74*x^24 + 118*x^23 + 40*x^22 + 46*x^21 + 20*x^20 + 51*x^19 + 8*x^18 + 59*x^17 + 86*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 22*x^8 + 38*x^7 + 8*x^6 + 62*x^5 + 20*x^4 + 21*x^3 + 40*x^2 + 61*x + 10, x^27 + 33*x^25 + 78*x^24 + 118*x^23 + 72*x^22 + 14*x^21 + 76*x^20 + 115*x^19 + 8*x^18 + 27*x^17 + 34*x^16 + 4*x^15 + 16*x^14 + 116*x^13 + 104*x^12 + 23*x^11 + 80*x^10 + 7*x^9 + 114*x^8 + 38*x^7 + 40*x^6 + 30*x^5 + 12*x^4 + 85*x^3 + 40*x^2 + 29*x + 94, x^27 + 33*x^25 + 22*x^24 + 22*x^23 + 56*x^22 + 78*x^21 + 12*x^20 + 19*x^19 + 24*x^18 + 27*x^17 + 106*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 74*x^8 + 70*x^7 + 88*x^6 + 94*x^5 + 12*x^4 + 117*x^3 + 120*x^2 + 29*x + 118, x^27 + 33*x^25 + 90*x^24 + 118*x^23 + 104*x^22 + 46*x^21 + 52*x^20 + 51*x^19 + 72*x^18 + 59*x^17 + 70*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 88*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 6*x^8 + 38*x^7 + 72*x^6 + 62*x^5 + 52*x^4 + 21*x^3 + 104*x^2 + 61*x + 26, x^27 + 33*x^25 + 26*x^24 + 6*x^23 + 24*x^22 + 62*x^21 + 36*x^20 + 35*x^19 + 24*x^18 + 43*x^17 + 22*x^16 + 36*x^15 + 48*x^14 + 84*x^13 + 56*x^12 + 119*x^11 + 112*x^10 + 39*x^9 + 102*x^8 + 118*x^7 + 56*x^6 + 14*x^5 + 100*x^4 + 69*x^3 + 120*x^2 + 109*x + 42, x^27 + 33*x^25 + 18*x^24 + 22*x^23 + 120*x^22 + 46*x^21 + 52*x^20 + 83*x^19 + 56*x^18 + 123*x^17 + 62*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 46*x^8 + 70*x^7 + 24*x^6 + 62*x^5 + 116*x^4 + 53*x^3 + 24*x^2 + 125*x + 66, x^27 + 33*x^25 + 14*x^24 + 6*x^23 + 120*x^22 + 30*x^21 + 60*x^20 + 99*x^19 + 88*x^18 + 11*x^17 + 114*x^16 + 36*x^15 + 112*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 112*x^10 + 103*x^9 + 82*x^8 + 118*x^7 + 24*x^6 + 110*x^5 + 60*x^4 + 5*x^3 + 56*x^2 + 77*x + 110, x^27 + 33*x^25 + 114*x^24 + 70*x^23 + 72*x^22 + 94*x^21 + 4*x^20 + 35*x^19 + 104*x^18 + 75*x^17 + 78*x^16 + 36*x^15 + 16*x^14 + 20*x^13 + 56*x^12 + 119*x^11 + 16*x^10 + 103*x^9 + 46*x^8 + 54*x^7 + 40*x^6 + 46*x^5 + 4*x^4 + 69*x^3 + 8*x^2 + 13*x + 82, x^27 + 33*x^25 + 82*x^24 + 102*x^23 + 40*x^22 + 126*x^21 + 36*x^20 + 3*x^19 + 8*x^18 + 43*x^17 + 14*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 120*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 14*x^8 + 86*x^7 + 8*x^6 + 78*x^5 + 36*x^4 + 37*x^3 + 40*x^2 + 109*x + 82, x^27 + 33*x^25 + 90*x^24 + 54*x^23 + 72*x^22 + 46*x^21 + 84*x^20 + 115*x^19 + 104*x^18 + 59*x^17 + 38*x^16 + 4*x^15 + 16*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 16*x^10 + 71*x^9 + 70*x^8 + 102*x^7 + 40*x^6 + 62*x^5 + 84*x^4 + 85*x^3 + 8*x^2 + 61*x + 122, x^27 + 33*x^25 + 66*x^24 + 54*x^23 + 24*x^22 + 78*x^21 + 116*x^20 + 51*x^19 + 24*x^18 + 91*x^17 + 46*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 62*x^8 + 102*x^7 + 56*x^6 + 94*x^5 + 52*x^4 + 21*x^3 + 120*x^2 + 93*x + 18, x^27 + 33*x^25 + 126*x^24 + 6*x^23 + 24*x^22 + 30*x^21 + 124*x^20 + 99*x^19 + 56*x^18 + 11*x^17 + 34*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 34*x^8 + 118*x^7 + 56*x^6 + 110*x^5 + 124*x^4 + 5*x^3 + 24*x^2 + 77*x + 126, x^27 + 33*x^25 + 22*x^24 + 70*x^23 + 104*x^22 + 126*x^21 + 124*x^20 + 99*x^19 + 104*x^18 + 107*x^17 + 122*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 8*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 106*x^8 + 54*x^7 + 72*x^6 + 78*x^5 + 60*x^4 + 5*x^3 + 8*x^2 + 45*x + 70, x^27 + 33*x^25 + 54*x^24 + 86*x^23 + 120*x^22 + 14*x^21 + 12*x^20 + 83*x^19 + 88*x^18 + 91*x^17 + 10*x^16 + 68*x^15 + 112*x^14 + 116*x^13 + 40*x^12 + 87*x^11 + 112*x^10 + 7*x^9 + 42*x^8 + 6*x^7 + 24*x^6 + 30*x^5 + 12*x^4 + 53*x^3 + 56*x^2 + 93*x + 86, x^27 + 33*x^25 + 18*x^24 + 118*x^23 + 88*x^22 + 78*x^21 + 84*x^20 + 115*x^19 + 88*x^18 + 91*x^17 + 30*x^16 + 4*x^15 + 48*x^14 + 116*x^13 + 88*x^12 + 23*x^11 + 112*x^10 + 7*x^9 + 110*x^8 + 38*x^7 + 120*x^6 + 94*x^5 + 20*x^4 + 85*x^3 + 56*x^2 + 93*x + 34, x^27 + 33*x^25 + 66*x^24 + 102*x^23 + 104*x^22 + 126*x^21 + 4*x^20 + 3*x^19 + 72*x^18 + 43*x^17 + 30*x^16 + 100*x^15 + 80*x^14 + 84*x^13 + 56*x^12 + 55*x^11 + 80*x^10 + 39*x^9 + 30*x^8 + 86*x^7 + 72*x^6 + 78*x^5 + 4*x^4 + 37*x^3 + 104*x^2 + 109*x + 66, x^27 + 33*x^25 + 50*x^24 + 22*x^23 + 120*x^22 + 110*x^21 + 52*x^20 + 83*x^19 + 56*x^18 + 59*x^17 + 94*x^16 + 68*x^15 + 112*x^14 + 52*x^13 + 24*x^12 + 87*x^11 + 48*x^10 + 71*x^9 + 14*x^8 + 70*x^7 + 24*x^6 + 126*x^5 + 116*x^4 + 53*x^3 + 24*x^2 + 61*x + 34, x^27 + 33*x^25 + 94*x^24 + 70*x^23 + 88*x^22 + 30*x^21 + 60*x^20 + 35*x^19 + 120*x^18 + 11*x^17 + 66*x^16 + 36*x^15 + 48*x^14 + 20*x^13 + 72*x^12 + 119*x^11 + 48*x^10 + 103*x^9 + 66*x^8 + 54*x^7 + 120*x^6 + 110*x^5 + 60*x^4 + 69*x^3 + 88*x^2 + 77*x + 94, x^27 + 33*x^25 + 110*x^24 + 86*x^23 + 72*x^22 + 110*x^21 + 12*x^20 + 19*x^19 + 8*x^18 + 59*x^17 + 2*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 104*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 82*x^8 + 6*x^7 + 40*x^6 + 126*x^5 + 76*x^4 + 117*x^3 + 40*x^2 + 61*x + 126, x^27 + 33*x^25 + 6*x^24 + 54*x^23 + 56*x^22 + 46*x^21 + 108*x^20 + 115*x^19 + 24*x^18 + 59*x^17 + 122*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 90*x^8 + 102*x^7 + 88*x^6 + 62*x^5 + 108*x^4 + 85*x^3 + 120*x^2 + 61*x + 102, x^27 + 33*x^25 + 42*x^24 + 118*x^23 + 40*x^22 + 46*x^21 + 84*x^20 + 51*x^19 + 8*x^18 + 59*x^17 + 118*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 54*x^8 + 38*x^7 + 8*x^6 + 62*x^5 + 84*x^4 + 21*x^3 + 40*x^2 + 61*x + 106, x^27 + 33*x^25 + 106*x^24 + 54*x^23 + 104*x^22 + 46*x^21 + 84*x^20 + 115*x^19 + 72*x^18 + 59*x^17 + 54*x^16 + 4*x^15 + 80*x^14 + 52*x^13 + 24*x^12 + 23*x^11 + 80*x^10 + 71*x^9 + 118*x^8 + 102*x^7 + 72*x^6 + 62*x^5 + 84*x^4 + 85*x^3 + 104*x^2 + 61*x + 42, x^27 + 33*x^25 + 126*x^24 + 86*x^23 + 72*x^22 + 46*x^21 + 44*x^20 + 19*x^19 + 8*x^18 + 123*x^17 + 114*x^16 + 68*x^15 + 16*x^14 + 52*x^13 + 40*x^12 + 87*x^11 + 80*x^10 + 71*x^9 + 66*x^8 + 6*x^7 + 40*x^6 + 62*x^5 + 108*x^4 + 117*x^3 + 40*x^2 + 125*x + 14, x^27 + 33*x^25 + 90*x^24 + 22*x^23 + 8*x^22 + 14*x^21 + 20*x^20 + 19*x^19 + 40*x^18 + 91*x^17 + 102*x^16 + 68*x^15 + 16*x^14 + 116*x^13 + 24*x^12 + 87*x^11 + 16*x^10 + 7*x^9 + 70*x^8 + 70*x^7 + 104*x^6 + 30*x^5 + 20*x^4 + 117*x^3 + 72*x^2 + 93*x + 58, x^27 + 33*x^25 + 78*x^24 + 102*x^23 + 88*x^22 + 126*x^21 + 28*x^20 + 3*x^19 + 120*x^18 + 43*x^17 + 82*x^16 + 100*x^15 + 48*x^14 + 84*x^13 + 8*x^12 + 55*x^11 + 48*x^10 + 39*x^9 + 82*x^8 + 86*x^7 + 120*x^6 + 78*x^5 + 28*x^4 + 37*x^3 + 88*x^2 + 109*x + 78, x^27 + 33*x^25 + 70*x^24 + 70*x^23 + 40*x^22 + 126*x^21 + 92*x^20 + 99*x^19 + 40*x^18 + 107*x^17 + 74*x^16 + 36*x^15 + 80*x^14 + 84*x^13 + 72*x^12 + 119*x^11 + 16*x^10 + 39*x^9 + 58*x^8 + 54*x^7 + 8*x^6 + 78*x^5 + 28*x^4 + 5*x^3 + 72*x^2 + 45*x + 118, x^27 + 33*x^25 + 50*x^24 + 54*x^23 + 56*x^22 + 14*x^21 + 116*x^20 + 51*x^19 + 120*x^18 + 27*x^17 + 30*x^16 + 4*x^15 + 112*x^14 + 116*x^13 + 24*x^12 + 23*x^11 + 48*x^10 + 7*x^9 + 14*x^8 + 102*x^7 + 88*x^6 + 30*x^5 + 52*x^4 + 21*x^3 + 88*x^2 + 29*x + 98, x^27 + 33*x^25 + 102*x^24 + 118*x^23 + 56*x^22 + 110*x^21 + 44*x^20 + 51*x^19 + 24*x^18 + 123*x^17 + 26*x^16 + 4*x^15 + 112*x^14 + 52*x^13 + 104*x^12 + 23*x^11 + 112*x^10 + 71*x^9 + 122*x^8 + 38*x^7 + 88*x^6 + 126*x^5 + 44*x^4 + 21*x^3 + 120*x^2 + 125*x + 70}


In [16]:
# get candidates for 29 lines
def lem62Polynomials():
	R.<x>=PolynomialRing(QQ)
	cand29=getCoeffsWeaklyType2(10,[1,-65,1884])
	cand29shift=[R(list(reversed(l)))(x+1) for l in cand29]
	cand29list=[list(reversed(l.coefficients(sparse=False))) for l in cand29shift]
	return listPowerReduceOddPC(cand29list,(x+5)^15*(x-5)^4,scc297,7)

def checkLemma62():
	R.<x>=PolynomialRing(QQ)
	print "--- Candidates for char poly corresponding to 29 lines ---"
	print ""
	tic = time.time()
	cand29red=lem62Polynomials()
	toc = time.time()
	print "Time taken to compute char poly candidates: " + str(toc-tic) + " seconds"
	print ""
	print "Candidates for char poly:"
	for i in range(len(cand29red)):
		ff=R(list(reversed(cand29red[i])))*(x+5)^15*(x-5)^4
		ms=R(ff/gcd(ff,ff.derivative()))
		print i+1, factor(ff)
	print ""
	cand29=[cand29red[i] for i in [0,30,24,22,4,2,20,28,29,14,25,27,12,9,3,17,15,13,23,19,26,8,11,21,18]]
	FarkasCertificates=[
	[44,0,0,423], 
	[-126,-631,0,0,-30576], 
	[0,-114,0,0,-11155], 
	[102,916,0,0,175136],
	[-366,-2563,0,0,-544242],
	[-2820, -12969, -59189, 0, 0, -34793172], 
	[361,1084,4712,0,0,1656424], 
	[0,0,2913,0,0,984942], 
	[76,75,67,0,0,0],
	[112,395,479,0,0,0], 
	[184,1105,6816,0,0,3452532], 
	[-52,-173,-157,0,0,0], 
	[-217, -1528, -11608, 0, 0, -6439670],
	[-71,-265,-339,0,0,0], 
	[0,676,3743,8141,0,0,0], 
	[-1018,0,8413,20451,0,0,0], 
	[0,0,3,-3784,0,0,-4921960], 
	[-2015, -14106, -98738, -690887, 0, 0, -899357723],
	[-242,0,-17,0,0,0,0], 
	[238,978,3367,6028,0,0,0], 
	[174,616,1795,2863,0,0,0], 
	[425, 1747, 6111, 11531, 0, 0, 0], 
	[8, -1000, -7250, -51880, -369160, 0, 0, -783400120], 
	[0, 2250, 25343, 212711, 1568930, 0, 0, 3329450510],
	[-2001, -7066, -19411, -27929, 0, 0, 0, 0]]
	bag=[]
	for i in range(len(cand29)):
		ff=R(list(reversed(cand29[i])))*(x+5)^15*(x-5)^4
		ms=R(ff/gcd(ff,ff.derivative()))
		g=R(ff.derivative()//gcd(ff,ff.derivative()))
		deg=ms.degree()
		f=ms+28*x^(deg-2)
		coeffs=list(reversed(f.coefficients(sparse=False)))
		gf=x^(deg-3)*R([coeffs[2],coeffs[1],coeffs[0]])
		ggf=gf(x-1)
		clist=list(reversed(ggf.coefficients(sparse=False)))
		print "------- Infeasibility of " + str(factor(ff)) + " -------"
		print ""
		tic = time.time()
		ll=getCoeffsType2(deg-1,[clist[0],clist[1],clist[2]])
		llpol=[R(list(reversed(l)))(x+1) for l in ll]
		ll2=[list(reversed(l.coefficients(sparse=False))) for l in llpol]
		bag+=[[factor(ff),listInterlaceReduce(ll2,ms)]]
		toc = time.time()
		print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
		print ""
		deg=ms.degree()
		numrows=len(bag[i][1])
		m=matrix(numrows,deg,[bag[i][1][j] for j in range(numrows)])
		gg=vector(list(reversed(g.coefficients(sparse=False))))
		print "Coefficient matrix A for interlacing char polys:"
		print m
		print ""
		mm=vector(list(reversed(FarkasCertificates[i])))
		print "Certificate of infeasibility c:"
		print "c = " + str(mm)
		ac=mm*m.transpose()
		print "Ac >= 0: " + str(isAtLeastZero(ac))
		print "Ac = " + str(ac)
		innerprod=sum([gg[j]*mm[j] for j in range(deg)])
		print "<g,c> < 0: " + str(innerprod < 0)
		print "<g,c> = " + str(innerprod)
		print ""

# check Lemma 6.3
# (x + 5)^15*(x-5)^10*(x -7)^2*(x^2 - 11*x + 16)
def lem63InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll=getCoeffsType2(4,[1,-22,156])
	llshift=[R(list(reversed(l)))(x+1) for l in ll]
	lllist=[list(reversed(l.coefficients(sparse=False))) for l in llshift]
	llred=listInterlaceReduce(lllist,(x + 5)*(x-5)*(x -7)*(x^2 - 11*x + 16))
	return listPowerReduce(llred,(x+5)^14*(x-5)^9*(x-7))

def checkLemma63():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x + 5)^15*(x-5)^10*(x -7)^2*(x^2 - 11*x + 16))) + "  ---"
	print ""
	tic = time.time()
	llSeidelred=lem63InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,5,[llSeidelred[j] for j in range(numrows)])
	mults=vector([15,10,2,1,1])
	N.<sqrt57>=NumberField(x^2 - 57)
	aln=(11+sqrt(11^2-4*16))/2
	NN.<z>=PolynomialRing(N)
	al=(11-sqrt57)/2
	froots=[-5,5,7,al,11-al]
	f=prod([(z-r) for r in froots])
	fbas=[NN(f/(z-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(5,5,[fbaslist[j] for j in range(5)])
	bb=mults*fbasm
	#submatrix of m without f1
	mf1=m[range(1,31),range(5)] 
	print "Matrix A' corresponding to interlacing polynomials without f1:" 
	print mf1
	print ""
	#Farkas certificate 
	fc1=vector([3936,0,0,29,0])  
	print "Certificate of warranty c for f1:"
	print "c = " + str(fc1)
	ac=fc1*mf1.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod=sum([fc1[j]*bb[j] for j in range(5)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	#submatrix of m without f2:
	mf2=m[[0,1,2,3]+range(5,31),range(5)]
	print "Matrix A' corresponding to interlacing polynomials without f2:" 
	print mf2
	print ""
	#Farkas certificate:
	fc2=vector([-333696,0,0,-2459,-492])
	print "Certificate of warranty c for f2:"
	print "c = " + str(fc2)   
	ac = fc2*mf2.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerproduct=sum([fc2[j]*bb[j] for j in range(5)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	f1=vector([m[0,j] for j in range(5)])
	f2=vector([m[4,j] for j in range(5)])
	af1=f1*fbasm^-1
	af2=f2*fbasm^-1
	print "angles for f1:"
	print af1
	print "angles for f2:"
	print af2

# check Lemma 6.4
# (x + 5)^15*(x-3)*(x-5)^9*(x -7)^2*(x^2 - 13*x + 32)
def lem64InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll=getCoeffsType2(5,[1,-28,288])
	llshift=[R(list(reversed(l)))(x+1) for l in ll]
	lllist=[list(reversed(l.coefficients(sparse=False))) for l in llshift]
	llred=listInterlaceReduce(lllist,(x + 5)*(x-3)*(x-5)*(x -7)*(x^2 - 13*x + 32))
	return listPowerReduce(llred,(x+5)^14*(x-5)^8*(x-7))

def checkLemma64():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x + 5)^15*(x-3)*(x-5)^9*(x -7)^2*(x^2 - 13*x + 32))) + "  ---"
	print ""
	tic = time.time()
	llSeidelred=lem64InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,6,[llSeidelred[j] for j in range(numrows)])
	mults=vector([15,1,9,2,1,1])
	N.<sqrt41>=NumberField(x^2 - 41)
	aln=(13+sqrt(13^2-4*32))/2
	NN.<z>=PolynomialRing(N)
	al=(13-sqrt41)/2
	froots=[-5,3,5,7,al,13-al]
	f=prod([(z-r) for r in froots])
	fbas=[NN(f/(z-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(6,6,[fbaslist[j] for j in range(6)])
	bb=mults*fbasm
	#submatrix of m without f1
	mf1=m[range(1,numrows),range(6)]
	print "Matrix A' corresponding to interlacing polynomials without f1:" 
	print mf1
	print ""
	#Farkas certificate 
	fc1=vector([0,0,0,-845,-703,-235])
	print "Certificate of warranty c for f1:"
	print "c = " + str(fc1)
	ac = fc1*mf1.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc1[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	#submatrix of m without f2:
	mf2=m[[0,1,2,3]+range(5,numrows),range(6)]
	print "Matrix A' corresponding to interlacing polynomials without f2:" 
	print mf2
	print ""
	#Farkas certificate:
	fc2=vector([-2729736,0,0,-6261,-1593,-433])
	print "Certificate of warranty c for f2:"
	print "c = " + str(fc2)  
	ac = fc2*mf2.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc2[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	f1=vector([m[0,j] for j in range(6)])
	f2=vector([m[4,j] for j in range(6)])
	af1=f1*fbasm^-1
	af2=f2*fbasm^-1
	print "angles for f1:"
	print af1
	print "angles for f2:"
	print af2
	

# check Lemma 6.5
# (x + 5)^15*(x-5)^10*(x -7)*(x^3-18*x^2 +93*x - 128)
def lem65InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll=getCoeffsType2(5,[1,-30,332])
	llshift=[R(list(reversed(l)))(x+1) for l in ll]
	lllist=[list(reversed(l.coefficients(sparse=False))) for l in llshift]
	llred=listInterlaceReduce(lllist,(x + 5)*(x-5)*(x -7)*(x^3-18*x^2 +93*x - 128))
	return listPowerReduce(llred,(x+5)^14*(x-5)^9)

def checkLemma65():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x + 5)^15*(x-5)^10*(x -7)*(x^3-18*x^2 +93*x - 128))) + "  ---"
	print ""
	tic = time.time()
	llSeidelred=lem65InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,6,[llSeidelred[j] for j in range(numrows)])
	mults=vector([15,10,1,1,1,1])
	N.<al>=NumberField(x^3-18*x^2 + 93*x -128)
	N1.<z>=PolynomialRing(N)
	N2.<be>=NumberField(z^2 + (al - 18)*z + al^2 - 18*al + 93)
	NN.<zz>=PolynomialRing(N2)
	froots=[-5,5,7,al,be,18-al-be]
	f=prod([(zz-r) for r in froots])
	fbas=[NN(f/(zz-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(6,6,[fbaslist[j] for j in range(6)])
	bb=mults*fbasm
	#submatrix of m without f1
	mf1=m[[0,1]+range(3,numrows),range(6)]  
	print "Matrix A' corresponding to interlacing polynomials without f1:" 
	print mf1
	print ""
	#Farkas certificate 
	fc1=vector([53248032,0,0,80553,12395,2066])
	print "Certificate of warranty c for f1:"
	print "c = " + str(fc1)
	ac = fc1*mf1.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc1[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(RR(innerprod) < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	#submatrix of m without f2:
	mf2=m[range(12)+range(13,numrows),range(6)]
	print "Matrix A' corresponding to interlacing polynomials without f2:" 
	print mf2
	print ""
	#Farkas certificate:
	fc2=vector([0,0,0,416,329,101])
	print "Certificate of warranty c for f2:"
	print "c = " + str(fc2)  
	ac = fc2*mf2.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc2[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(RR(innerprod) < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	f1=vector([m[2,j] for j in range(6)])
	f2=vector([m[12,j] for j in range(6)])
	af1=f1*fbasm^-1
	af2=f2*fbasm^-1
	print "angles for f1:"
	print af1
	print "angles for f2:"
	print af2


# check Lemma 6.6
# (x + 5)^15*(x-3)*(x-5)^11*(x^2-17*x +68)
def lem66InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll=getCoeffsType2(4,[1,-24,188])
	llshift=[R(list(reversed(l)))(x+1) for l in ll]
	lllist=[list(reversed(l.coefficients(sparse=False))) for l in llshift]
	llred=listInterlaceReduce(lllist,(x + 5)*(x-3)*(x-5)*(x^2-17*x +68))
	return listPowerReduce(llred,(x+5)^14*(x-5)^10)

def checkLemma66():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x + 5)^15*(x-3)*(x-5)^11*(x^2-17*x +68))) + "  ---"
	print ""
	tic = time.time()
	llSeidelred=lem66InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,5,[llSeidelred[j] for j in range(numrows)])
	mults=vector([15,1,11,1,1])
	N.<sqrt17>=NumberField(x^2 - 17)
	NN.<z>=PolynomialRing(N)
	al=(17+sqrt17)/2
	froots=[-5,3,5,al,17-al]
	f=prod([(z-r) for r in froots])
	fbas=[NN(f/(z-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(5,5,[fbaslist[j] for j in range(5)])
	bb=mults*fbasm
	#submatrix of m without f1
	mf1=m[range(10)+range(11,numrows),range(5)]
	print "Matrix A' corresponding to interlacing polynomials without f1:" 
	print mf1 
	print ""
	#Farkas certificate 
	fc1=vector([-256444,0,0,-1143,-190])
	print "Certificate of warranty c for f1:"
	print "c = " + str(fc1)  
	ac =  fc1*mf1.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc1[j]*bb[j] for j in range(5)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	f1=vector([m[10,j] for j in range(5)])
	af1=f1*fbasm^-1
	print "angles for f1:"
	print af1
	print ""

	print "--- checking for interlacing polynomials compatible with f1 ---"
	p=(z^2-25)
	for i in range(10)+range(11,numrows):
		#print i
		f2=vector([m[i,j] for j in range(5)])
		af2=f2*fbasm^-1
		roots1=(z^2-af2[1]*af1[1]).roots()
		if len(roots1) > 0:
			be1=roots1[0][0]
			roots2=(z^2-af2[3]*af1[3]).roots()
			if len(roots2) > 0:
				be2=roots2[0][0]
				roots3=(z^2-af2[4]*af1[4]).roots()
				if len(roots3) > 0:
					be3=roots3[0][0]
				else:
					continue
			else:
				L2.<be2>=NumberField(z^2-af2[3]*af1[3])
				LL3.<w3>=PolynomialRing(L2)
				roots3=(w3^2-af2[4]*af1[2]).roots()
				if len(roots3) > 0:
					be3=roots3[0][0]
				else:
					continue
		else:
			L1.<be1>=NumberField(z^2-af2[1]*af1[1])
			LL1.<w2>=PolynomialRing(L1)
			roots2=(w2^2-af2[3]*af1[3]).roots()
			if len(roots2) > 0:
				be2=roots2[0][0]
				roots3=(w2^2-af2[4]*af1[4]).roots()
				if len(roots3) > 0:
					be3=roots3[0][0]
				else:
					continue
			else:
				L2.<be2>=NumberField(w2^2-af2[3]*af1[3])
				LL3.<w3>=PolynomialRing(L2)
				roots3=(w3^2-af2[4]*af1[4]).roots()
				if len(roots3) > 0:
					be3=roots3[0][0]
				else:
					continue

		if p(3)*be1+p(al)*be2+p(17-al)*be3 in QQ or p(3)*be1+p(al)*be2-p(17-al)*be3 in QQ or p(3)*be1-p(al)*be2+p(17-al)*be3 in QQ or p(3)*be1-p(al)*be2-p(17-al)*be3 in QQ:  
			print str(factor(R(list(reversed(llSeidelred[i]))))) + " is compatible with f1"
	
	print "--- end of compatibility check ---"
	print ""
	#submatrix of m with only f1 and f2
	mmf1=m[[1,10],range(5)]  
	print "Matrix A'' corresponding to interlacing polynomials f1 and f2:" 
	print mmf1 
	print ""
	#Farkas certificate 
	ffc1=vector([0,0,0,-7,-46]) 
	print "Certificate of infeasibility c:"
	print "c = " + str(ffc1)   
	ac = ffc1*mmf1.transpose()
	print "A''c >= 0: " + str(isAtLeastZero(ac))
	print "A''c = " + str(ac)
	innerprod = sum([ffc1[j]*bb[j] for j in range(5)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
		

# check Lemma 6.7
# (x + 5)^15*(x-3)^2*(x-5)^8*(x-7)^2*(x^2-15*x +52)
def lem67InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll=getCoeffsType2(5,[1,-30,336])
	llshift=[R(list(reversed(l)))(x+1) for l in ll]
	lllist=[list(reversed(l.coefficients(sparse=False))) for l in llshift]
	llred=listInterlaceReduce(lllist, (x + 5)*(x-3)*(x-5)*(x-7)*(x^2-15*x +52))
	return listPowerReduce(llred,(x+5)^14*(x-3)*(x-5)^7*(x-7))

def checkLemma67():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x + 5)^15*(x-3)^2*(x-5)^8*(x-7)^2*(x^2-15*x +52))) + "  ---"
	print ""
	tic = time.time()
	llSeidelred=lem67InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,6,[llSeidelred[j] for j in range(numrows)])
	mults=vector([15,2,8,2,1,1])
	N.<sqrt17>=NumberField(x^2 - 17)
	al=(15-sqrt17)/2
	NN.<z>=PolynomialRing(N)
	froots=[-5,3,5,7,al,15-al]
	f=prod([(z-r) for r in froots])
	fbas=[NN(f/(z-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(6,6,[fbaslist[j] for j in range(6)])
	bb=mults*fbasm
	#submatrix of m without f1
	mf1=m[range(4)+range(5,numrows),range(6)]
	print "Matrix A' corresponding to interlacing polynomials without f1:" 
	print mf1  
	print ""
	#Farkas certificate 
	fc1=vector([0,0,0,708,507,154])
	print "Certificate of warranty c for f1:"
	print "c = " + str(fc1)   
	ac = fc1*mf1.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc1[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	#submatrix of m without f2:
	mf2=m[range(5)+range(6,numrows),range(6)]
	print "Matrix A' corresponding to interlacing polynomials without f2:" 
	print mf2
	print ""
	#Farkas certificate:
	fc2=vector([26302558,0,0,39525,6783,1196])
	print "Certificate of warranty c for f2:"
	print "c = " + str(fc2)    
	ac = fc2*mf2.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc2[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	f1=vector([m[4,j] for j in range(6)])
	f2=vector([m[5,j] for j in range(6)])
	af1=f1*fbasm^-1
	af2=f2*fbasm^-1
	p=(z^2-25)*(z-3)*(z-7)
	compat=[]
	print "--- checking for interlacing polynomials compatible with f1 and f2 ---"
	for i in range(numrows):
		f3=vector([m[i,j] for j in range(6)])
		af3=f3*fbasm^-1
		roots1=(z^2-af2[4]*af3[4]).roots()
		if len(roots1) > 0:
			al1=roots1[0][0]
			roots2=(z^2-af2[5]*af3[5]).roots()
			if len(roots2) > 0:
				al2=roots2[0][0]
			else:
				L2.<al2>=NumberField(z^2-af2[5]*af3[5])
		else:
			L1.<al1>=NumberField(z^2-af2[4]*af3[4])
			LL1.<zz>=PolynomialRing(L1)
			roots2=(zz^2-af2[5]*af3[5]).roots()
			if len(roots2) > 0:
				al2=roots2[0][0]
			else:
				L2.<al2>=NumberField(zz^2-af2[5]*af3[5])

		if (p(al)*al1+p(15-al)*al2) in QQ or (p(al)*al1-p(15-al)*al2) in QQ:
			compat+=[i]
			print str(factor(R(list(reversed(llSeidelred[i]))))) + " is compatible with f1 and f2"

	print "--- end of compatibility check ---"
	print ""

	m2=m[compat,range(6)]
	print "Matrix A' corresponding to compatible polynomials:" 
	print m2
	print ""

	nn=vector([0,0,20,7,1,1,0])
	print str(nn) + " times A' equals " + str(bb) + ": " + str(nn*m2 == bb)
	#adding to nn any nonzero vector in the left nullspace of m gives a vector with at least one negative entry
	print "Left kernel of A':" 
	print m2.left_kernel()
	print ""

	f3=vector([m[compat[4],j] for j in range(6)])
	f4=vector([m[compat[5],j] for j in range(6)])
	af3=f3*fbasm^-1
	af4=f4*fbasm^-1
	print "angles for f1:"
	print af1
	print "angles for f2:"
	print af2
	print "angles for f3:"
	print af3
	print "angles for f4:"
	print af4


# check Lemma 6.9
# (x + 5)^15*(x-3)*(x-4)*(x-5)^10*(x-9)^2
def lem69InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll=getCoeffsType2(4,[1,-20,132])
	llshift=[R(list(reversed(l)))(x+1) for l in ll]
	lllist=[list(reversed(l.coefficients(sparse=False))) for l in llshift]
	llred=listInterlaceReduce(lllist, (x + 5)*(x-3)*(x-4)*(x-5)*(x-9))
	return listPowerReduce(llred,(x+5)^14*(x-5)^9*(x-9))

def checkLemma69():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x + 5)^15*(x-3)*(x-4)*(x-5)^10*(x-9)^2)) + "  ---"
	print ""
	tic = time.time()
	llSeidelred=lem69InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	numrows=len(llSeidelred)
	m=matrix(numrows,5,[llSeidelred[j] for j in range(numrows)])
	mults=vector([15,1,1,10,2])
	froots=[-5,3,4,5,9]
	f=prod([(x-r) for r in froots])
	fbas=[R(f/(x-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(5,5,[fbaslist[j] for j in range(5)])
	bb=mults*fbasm
	m2=m[[0,1]+range(3,6),range(5)]
	print "Matrix A' corresponding to last 5 interlacing characteristic polynomials:" 
	print m2
	print ""
	nn=m2.solve_left(bb)
	print "solution to nA' = " + str(bb) + ":"
	print nn
	nn1=vector([25,0,0,2,2])
	nn2=vector([25,0,1,0,3])
	nn3=vector([24,2,0,0,3])
	print "left kernel of A':"
	print m2.left_kernel()
	print ""
	print "Check that the only nonnegative solutions to nA' = " + str(bb) + " are"
	print str(nn1) + ", " + str(nn2) + ", and " + str(nn3)
	print ""
	f1=vector([m2[0,j] for j in range(5)])
	f2=vector([m2[1,j] for j in range(5)])
	f3=vector([m2[2,j] for j in range(5)])
	f4=vector([m2[3,j] for j in range(5)])
	f5=vector([m2[4,j] for j in range(5)])
	af1=f1*fbasm^-1
	af2=f2*fbasm^-1
	af3=f3*fbasm^-1
	af4=f4*fbasm^-1
	af5=f5*fbasm^-1
	print "angles for f1:"
	print af1
	print "angles for f2:"
	print af2
	print "angles for f3:"
	print af3
	print "angles for f4:"
	print af4
	print "angles for f5:"
	print af5

# check Lemma 6.8
# (x + 5)^14*(x-5)^9*(x-9)*(x^2-4*x-1)*(x^2-12*x+31)
def lem68InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll2=getCoeffsWeaklyType2(6,[1,-31,364])
	llshift2=[R(list(reversed(l)))(x+1) for l in ll2]
	lllist2=[list(reversed(l.coefficients(sparse=False))) for l in llshift2]
	llred2=listInterlaceReduce(lllist2,(x+5)*(x-5)*(x-9)*(x^2-4*x-1)*(x^2-12*x+31))
	return listPowerReduceOddPC(llred2,(x+5)^13*(x-5)^8,scc277,7)

def checkLemma68():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x + 5)^14*(x-5)^9*(x-9)*(x^2-4*x-1)*(x^2-12*x+31))) + "  ---"
	print ""
	tic = time.time()
	llSeidelred2=lem68InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	numrows=len(llSeidelred2)
	m=matrix(numrows,7,[llSeidelred2[j] for j in range(numrows)])
	mults=vector([14,9,1,1,1,1,1])
	N.<sqrt5>=NumberField(x^2 - 5)
	al=2-sqrt5
	NN.<z>=PolynomialRing(N)
	froots=[-5,5,9,al,4-al,4+al,8-al]
	f=prod([(z-r) for r in froots])
	fbas=[NN(f/(z-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(7,7,[fbaslist[j] for j in range(7)])
	bb=mults*fbasm
	#submatrix of m without f1
	mf1=m[range(1,numrows),range(7)] 
	print "Matrix A' corresponding to interlacing polynomials without f1:" 
	print mf1
	print ""
	#Farkas certificate 
	fc1=vector([0,0,0,-7130,-5303,-1486,-344])
	print "Certificate of warranty c for f1:"
	print "c = " + str(fc1)    
	ac = fc1*mf1.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	
	innerprod = sum([fc1[j]*bb[j] for j in range(7)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	f1=vector([m[0,j] for j in range(7)])
	af1=f1*fbasm^-1
	print "angles for f1:"
	print af1
	print ""
	print "--- checking for interlacing polynomials compatible with f1 ---"
	p=(z^2-25)
	compat=[]
	for i in range(numrows):
		print str(i+1) + "/" + str(numrows)
		f2=vector([m[i,j] for j in range(7)])
		af2=f2*fbasm^-1
		roots1=(z^2-af1[2]*af2[2]).roots()
		if len(roots1) > 0:
			al1=roots1[0][0]
			roots2=(z^2-af1[3]*af2[3]).roots()
			if len(roots2) > 0:
				al2=roots2[0][0]
				roots3=(z^2-af1[4]*af2[4]).roots()
				if len(roots3) > 0:
					al3=roots3[0][0]
					roots4=(z^2-af1[5]*af2[5]).roots()
					if len(roots4) > 0:
						al4=roots4[0][0]
						roots5=(z^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
					else:
						L4.<al4>=NumberField(z^2-af1[5]*af2[5])
						LL4.<z4>=PolynomialRing(L4)
						roots5=(z4^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
				else:
					L3.<al3>=NumberField(z^2-af1[4]*af2[4])
					LL3.<z3>=PolynomialRing(L3)
					roots4=(z3^2-af1[5]*af2[5]).roots()
					if len(roots4) > 0:
						al4=roots4[0][0]
						roots5=(z3^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
					else:
						L4.<al4>=NumberField(z3^2-af1[5]*af2[5])
						LL4.<z4>=PolynomialRing(L4)
						roots5=(z4^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
			else:
				L2.<al2>=NumberField(z^2-af1[3]*af2[3])
				LL2.<z2>=PolynomialRing(L2)
				roots3=(z2^2-af1[4]*af2[4]).roots()
				if len(roots3) > 0:
					al3=roots3[0][0]
					roots4=(z2^2-af1[5]*af2[5]).roots()
					if len(roots4) > 0:
						al4=roots4[0][0]
						roots5=(z2^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
					else:
						L4.<al4>=NumberField(z2^2-af1[5]*af2[5])
						LL4.<z4>=PolynomialRing(L4)
						roots5=(z4^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
				else:
					L3.<al3>=NumberField(z2^2-af1[4]*af2[4])
					LL3.<z3>=PolynomialRing(L3)
					roots4=(z3^2-af1[5]*af2[5]).roots()
					if len(roots4) > 0:
						al4=roots4[0][0]
						roots5=(z3^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
					else:
						L4.<al4>=NumberField(z3^2-af1[5]*af2[5])
						LL4.<z4>=PolynomialRing(L4)
						roots5=(z4^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
		else:
			L1.<al1>=NumberField(z^2-af1[2]*af2[2])
			LL1.<z1>=PolynomialRing(L1)
			roots2=(z1^2-af1[3]*af2[3]).roots()
			if len(roots2) >0:
				al2=roots2[0][0]
				roots3=(z1^2-af1[4]*af2[4]).roots()
				if len(roots3) > 0:
					al3=roots3[0][0]
					roots4=(z1^2-af1[5]*af2[5]).roots()
					if len(roots4) > 0:
						al4=roots4[0][0]
						roots5=(z1^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
					else:
						L4.<al4>=NumberField(z1^2-af1[5]*af2[5])
						LL4.<z4>=PolynomialRing(L4)
						roots5=(z4^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
				else:
					L3.<al3>=NumberField(z^2-af1[4]*af2[4])
					LL3.<z3>=PolynomialRing(L3)
					roots4=(z3^2-af1[5]*af2[5]).roots()
					if len(roots4) > 0:
						al4=roots4[0][0]
						roots5=(z3^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
					else:
						L4.<al4>=NumberField(z3^2-af1[5]*af2[5])
						LL4.<z4>=PolynomialRing(L4)
						roots5=(z4^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
			else:
				L2.<al2>=NumberField(z1^2-af1[3]*af2[3])
				LL2.<z2>=PolynomialRing(L2)
				roots3=(z2^2-af1[4]*af2[4]).roots()
				if len(roots3) > 0:
					al3=roots3[0][0]
					roots4=(z2^2-af1[5]*af2[5]).roots()
					if len(roots4) > 0:
						al4=roots4[0][0]
						roots5=(z2^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							L5.<al5>=NumberField(z2^2-af1[6]*af2[6])
					else:
						L4.<al4>=NumberField(z2^2-af1[5]*af2[5])
						LL4.<z4>=PolynomialRing(L4)
						roots5=(z4^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
				else:
					L3.<al3>=NumberField(z2^2-af1[4]*af2[4])
					LL3.<z3>=PolynomialRing(L3)
					roots4=(z3^2-af1[5]*af2[5]).roots()
					if len(roots4) > 0:
						al4=roots4[0][0]
						roots5=(z3^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							L5.<al5>=NumberField(z3^2-af1[6]*af2[6])
					else:
						L4.<al4>=NumberField(z3^2-af1[5]*af2[5])
						LL4.<z4>=PolynomialRing(L4)
						roots5=(z4^2-af1[6]*af2[6]).roots()
						if len(roots5) > 0:
							al5=roots5[0][0]
						else:
							continue
		uss={1,-1}
		cp=cartesian_product([uss,uss,uss,uss,uss])
		elmnts=[p(9)*al1,p(al)*al2,p(4-al)*al3,p(4+al)*al4,p(8-al)*al5]
		flag=False
		for mtpl in cp:
			if flag:
				continue
			if sum([mtpl[itr]*elmnts[itr] for itr in range(5)]) in QQ:
				flag = True
		if flag:
		 	compat+=[i]
		 	print str(factor(R(list(reversed(llSeidelred2[i]))))) + " is compatible with f1"

	print "--- end of compatibility check ---"
	print ""
	m2=m[compat,range(7)]
	print "Matrix A' corresponding to compatible polynomials:" 
	print m2
	print ""

	print "Solution to nA' = " + str(bb) + ":"
	print m2.solve_left(bb)
	print ""
	print "Left kernel of A':"
	print m2.left_kernel()


In [17]:
#precompute Seidel char polys classes n=41, e=7
#scc417=SeidelCharPolysMod(41,7)

In [18]:
scc417={x^41 + 76*x^39 + 108*x^38 + 102*x^37 + 20*x^36 + 28*x^35 + 116*x^34 + 21*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 38*x^5 + 52*x^4 + 124*x^3 + 84*x^2 + 105*x + 44, x^41 + 76*x^39 + 28*x^38 + 6*x^37 + 4*x^36 + 92*x^35 + 4*x^34 + 53*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 70*x^5 + 36*x^4 + 60*x^3 + 100*x^2 + 9*x + 124, x^41 + 76*x^39 + 48*x^38 + 30*x^37 + 80*x^36 + 44*x^35 + 80*x^34 + 13*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 30*x^5 + 80*x^4 + 12*x^3 + 80*x^2 + 33*x + 48, x^41 + 76*x^39 + 84*x^38 + 102*x^37 + 76*x^36 + 28*x^35 + 12*x^34 + 21*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 38*x^5 + 44*x^4 + 124*x^3 + 44*x^2 + 105*x + 52, x^41 + 76*x^39 + 20*x^38 + 38*x^37 + 44*x^36 + 28*x^35 + 12*x^34 + 85*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 102*x^5 + 12*x^4 + 124*x^3 + 44*x^2 + 41*x + 20, x^41 + 76*x^39 + 40*x^38 + 78*x^37 + 72*x^36 + 76*x^35 + 56*x^34 + 61*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 78*x^5 + 8*x^4 + 44*x^3 + 120*x^2 + 81*x + 24, x^41 + 76*x^39 + 56*x^38 + 14*x^37 + 24*x^36 + 76*x^35 + 104*x^34 + 125*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 14*x^5 + 88*x^4 + 44*x^3 + 40*x^2 + 17*x + 8, x^41 + 76*x^39 + 40*x^38 + 110*x^37 + 104*x^36 + 12*x^35 + 120*x^34 + 93*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 110*x^5 + 40*x^4 + 108*x^3 + 56*x^2 + 113*x + 56, x^41 + 76*x^39 + 24*x^38 + 62*x^37 + 72*x^36 + 44*x^35 + 104*x^34 + 109*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 62*x^5 + 8*x^4 + 12*x^3 + 40*x^2 + x + 120, x^41 + 76*x^39 + 68*x^38 + 118*x^37 + 44*x^36 + 124*x^35 + 60*x^34 + 37*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 54*x^5 + 12*x^4 + 92*x^3 + 92*x^2 + 121*x + 52, x^41 + 76*x^39 + 92*x^38 + 118*x^37 + 116*x^36 + 60*x^35 + 100*x^34 + 101*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 54*x^5 + 20*x^4 + 28*x^3 + 68*x^2 + 57*x + 108, x^41 + 76*x^39 + 80*x^38 + 78*x^37 + 96*x^36 + 12*x^35 + 80*x^34 + 125*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 78*x^5 + 96*x^4 + 108*x^3 + 80*x^2 + 17*x, x^41 + 76*x^39 + 96*x^38 + 110*x^37 + 48*x^36 + 76*x^35 + 29*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 110*x^5 + 48*x^4 + 44*x^3 + 49*x + 112, x^41 + 76*x^39 + 48*x^38 + 110*x^37 + 64*x^36 + 76*x^35 + 112*x^34 + 29*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 110*x^5 + 64*x^4 + 44*x^3 + 112*x^2 + 49*x + 32, x^41 + 76*x^39 + 60*x^38 + 22*x^37 + 52*x^36 + 60*x^35 + 4*x^34 + 69*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 86*x^5 + 84*x^4 + 28*x^3 + 100*x^2 + 25*x + 44, x^41 + 76*x^39 + 72*x^38 + 62*x^37 + 24*x^36 + 44*x^35 + 56*x^34 + 109*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 62*x^5 + 88*x^4 + 12*x^3 + 120*x^2 + x + 40, x^41 + 76*x^39 + 112*x^38 + 30*x^37 + 80*x^36 + 44*x^35 + 16*x^34 + 13*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 30*x^5 + 80*x^4 + 12*x^3 + 16*x^2 + 33*x + 48, x^41 + 76*x^39 + 40*x^38 + 46*x^37 + 72*x^36 + 76*x^35 + 120*x^34 + 93*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 46*x^5 + 8*x^4 + 44*x^3 + 56*x^2 + 113*x + 88, x^41 + 76*x^39 + 28*x^38 + 70*x^37 + 68*x^36 + 92*x^35 + 4*x^34 + 117*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 6*x^5 + 100*x^4 + 60*x^3 + 100*x^2 + 73*x + 60, x^41 + 76*x^39 + 88*x^38 + 126*x^37 + 8*x^36 + 108*x^35 + 104*x^34 + 109*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 126*x^5 + 72*x^4 + 76*x^3 + 40*x^2 + x + 120, x^41 + 76*x^39 + 64*x^38 + 78*x^37 + 48*x^36 + 12*x^35 + 96*x^34 + 125*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 78*x^5 + 48*x^4 + 108*x^3 + 96*x^2 + 17*x + 48, x^41 + 76*x^39 + 104*x^38 + 30*x^37 + 24*x^36 + 44*x^35 + 24*x^34 + 13*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 30*x^5 + 88*x^4 + 12*x^3 + 88*x^2 + 33*x + 40, x^41 + 76*x^39 + 72*x^38 + 46*x^37 + 72*x^36 + 76*x^35 + 24*x^34 + 93*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 46*x^5 + 8*x^4 + 44*x^3 + 88*x^2 + 113*x + 24, x^41 + 76*x^39 + 120*x^38 + 46*x^37 + 120*x^36 + 76*x^35 + 40*x^34 + 93*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 46*x^5 + 56*x^4 + 44*x^3 + 104*x^2 + 113*x + 40, x^41 + 76*x^39 + 108*x^38 + 70*x^37 + 116*x^36 + 92*x^35 + 52*x^34 + 117*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 6*x^5 + 20*x^4 + 60*x^3 + 20*x^2 + 73*x + 12, x^41 + 76*x^39 + 96*x^38 + 78*x^37 + 80*x^36 + 76*x^35 + 61*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 78*x^5 + 80*x^4 + 44*x^3 + 81*x + 80, x^41 + 76*x^39 + 104*x^38 + 126*x^37 + 56*x^36 + 44*x^35 + 24*x^34 + 45*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 126*x^5 + 120*x^4 + 12*x^3 + 88*x^2 + 65*x + 8, x^41 + 76*x^39 + 80*x^38 + 110*x^37 + 32*x^36 + 76*x^35 + 80*x^34 + 29*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 110*x^5 + 32*x^4 + 44*x^3 + 80*x^2 + 49*x + 64, x^41 + 76*x^39 + 80*x^38 + 126*x^37 + 80*x^36 + 44*x^35 + 48*x^34 + 45*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 126*x^5 + 80*x^4 + 12*x^3 + 48*x^2 + 65*x + 48, x^41 + 76*x^39 + 80*x^38 + 94*x^37 + 16*x^36 + 108*x^35 + 48*x^34 + 13*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 94*x^5 + 16*x^4 + 76*x^3 + 48*x^2 + 33*x + 112, x^41 + 76*x^39 + 80*x^38 + 126*x^37 + 48*x^36 + 44*x^35 + 112*x^34 + 45*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 126*x^5 + 48*x^4 + 12*x^3 + 112*x^2 + 65*x + 16, x^41 + 76*x^39 + 100*x^38 + 102*x^37 + 124*x^36 + 92*x^35 + 60*x^34 + 85*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 38*x^5 + 92*x^4 + 60*x^3 + 92*x^2 + 41*x + 68, x^41 + 76*x^39 + 20*x^38 + 54*x^37 + 92*x^36 + 124*x^35 + 108*x^34 + 101*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 118*x^5 + 60*x^4 + 92*x^3 + 12*x^2 + 57*x + 4, x^41 + 76*x^39 + 96*x^38 + 110*x^37 + 112*x^36 + 76*x^35 + 29*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 110*x^5 + 112*x^4 + 44*x^3 + 49*x + 48, x^41 + 76*x^39 + 68*x^38 + 118*x^37 + 76*x^36 + 60*x^35 + 60*x^34 + 101*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 54*x^5 + 44*x^4 + 28*x^3 + 92*x^2 + 57*x + 20, x^41 + 76*x^39 + 48*x^38 + 94*x^37 + 48*x^36 + 44*x^35 + 16*x^34 + 77*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 94*x^5 + 48*x^4 + 12*x^3 + 16*x^2 + 97*x + 16, x^41 + 76*x^39 + 60*x^38 + 54*x^37 + 116*x^36 + 124*x^35 + 4*x^34 + 101*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 118*x^5 + 20*x^4 + 92*x^3 + 100*x^2 + 57*x + 108, x^41 + 76*x^39 + 56*x^38 + 110*x^37 + 88*x^36 + 76*x^35 + 40*x^34 + 29*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 110*x^5 + 24*x^4 + 44*x^3 + 104*x^2 + 49*x + 8, x^41 + 76*x^39 + 92*x^38 + 6*x^37 + 68*x^36 + 92*x^35 + 68*x^34 + 53*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 70*x^5 + 100*x^4 + 60*x^3 + 36*x^2 + 9*x + 60, x^41 + 76*x^39 + 120*x^38 + 14*x^37 + 56*x^36 + 12*x^35 + 40*x^34 + 61*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 14*x^5 + 120*x^4 + 108*x^3 + 104*x^2 + 81*x + 104, x^41 + 76*x^39 + 12*x^38 + 6*x^37 + 84*x^36 + 92*x^35 + 20*x^34 + 53*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 70*x^5 + 116*x^4 + 60*x^3 + 116*x^2 + 9*x + 44, x^41 + 76*x^39 + 88*x^38 + 126*x^37 + 72*x^36 + 108*x^35 + 104*x^34 + 109*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 126*x^5 + 8*x^4 + 76*x^3 + 40*x^2 + x + 56, x^41 + 76*x^39 + 64*x^38 + 14*x^37 + 112*x^36 + 76*x^35 + 32*x^34 + 125*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 14*x^5 + 112*x^4 + 44*x^3 + 32*x^2 + 17*x + 48, x^41 + 76*x^39 + 64*x^38 + 62*x^37 + 96*x^36 + 108*x^35 + 45*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 62*x^5 + 96*x^4 + 76*x^3 + 65*x + 96, x^41 + 76*x^39 + 52*x^38 + 70*x^37 + 76*x^36 + 92*x^35 + 108*x^34 + 117*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 6*x^5 + 44*x^4 + 60*x^3 + 12*x^2 + 73*x + 116, x^41 + 76*x^39 + 12*x^38 + 70*x^37 + 52*x^36 + 92*x^35 + 84*x^34 + 117*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 6*x^5 + 84*x^4 + 60*x^3 + 52*x^2 + 73*x + 12, x^41 + 76*x^39 + 62*x^37 + 64*x^36 + 108*x^35 + 45*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 62*x^5 + 64*x^4 + 76*x^3 + 65*x + 64, x^41 + 76*x^39 + 24*x^38 + 46*x^37 + 24*x^36 + 12*x^35 + 72*x^34 + 29*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 46*x^5 + 88*x^4 + 108*x^3 + 8*x^2 + 49*x + 72, x^41 + 76*x^39 + 44*x^38 + 102*x^37 + 20*x^36 + 92*x^35 + 116*x^34 + 85*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 38*x^5 + 52*x^4 + 60*x^3 + 84*x^2 + 41*x + 108, x^41 + 76*x^39 + 52*x^38 + 70*x^37 + 12*x^36 + 92*x^35 + 108*x^34 + 117*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 6*x^5 + 108*x^4 + 60*x^3 + 12*x^2 + 73*x + 52, x^41 + 76*x^39 + 92*x^38 + 70*x^37 + 100*x^36 + 28*x^35 + 68*x^34 + 53*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 6*x^5 + 4*x^4 + 124*x^3 + 36*x^2 + 9*x + 28, x^41 + 76*x^39 + 112*x^38 + 94*x^37 + 16*x^36 + 108*x^35 + 80*x^34 + 13*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 94*x^5 + 16*x^4 + 76*x^3 + 80*x^2 + 33*x + 48, x^41 + 76*x^39 + 20*x^38 + 54*x^37 + 28*x^36 + 60*x^35 + 44*x^34 + 37*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 118*x^5 + 124*x^4 + 28*x^3 + 76*x^2 + 121*x + 4, x^41 + 76*x^39 + 72*x^38 + 14*x^37 + 104*x^36 + 76*x^35 + 24*x^34 + 125*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 14*x^5 + 40*x^4 + 44*x^3 + 88*x^2 + 17*x + 120, x^41 + 76*x^39 + 68*x^38 + 6*x^37 + 60*x^36 + 92*x^35 + 92*x^34 + 53*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 70*x^5 + 28*x^4 + 60*x^3 + 124*x^2 + 9*x + 4, x^41 + 76*x^39 + 120*x^38 + 94*x^37 + 104*x^36 + 44*x^35 + 72*x^34 + 77*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 94*x^5 + 40*x^4 + 12*x^3 + 8*x^2 + 97*x + 24, x^41 + 76*x^39 + 64*x^38 + 30*x^37 + 64*x^36 + 44*x^35 + 64*x^34 + 13*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 30*x^5 + 64*x^4 + 12*x^3 + 64*x^2 + 33*x + 64, x^41 + 76*x^39 + 4*x^38 + 38*x^37 + 124*x^36 + 28*x^35 + 28*x^34 + 85*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 102*x^5 + 92*x^4 + 124*x^3 + 60*x^2 + 41*x + 68, x^41 + 76*x^39 + 56*x^38 + 110*x^37 + 88*x^36 + 12*x^35 + 104*x^34 + 93*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 110*x^5 + 24*x^4 + 108*x^3 + 40*x^2 + 113*x + 72, x^41 + 76*x^39 + 104*x^38 + 30*x^37 + 88*x^36 + 44*x^35 + 24*x^34 + 13*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 30*x^5 + 24*x^4 + 12*x^3 + 88*x^2 + 33*x + 104, x^41 + 76*x^39 + 28*x^38 + 22*x^37 + 52*x^36 + 60*x^35 + 100*x^34 + 69*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 86*x^5 + 84*x^4 + 28*x^3 + 68*x^2 + 25*x + 108, x^41 + 76*x^39 + 28*x^38 + 22*x^37 + 84*x^36 + 124*x^35 + 100*x^34 + 5*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 86*x^5 + 116*x^4 + 92*x^3 + 68*x^2 + 89*x + 76, x^41 + 76*x^39 + 104*x^38 + 126*x^37 + 88*x^36 + 108*x^35 + 24*x^34 + 109*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 126*x^5 + 24*x^4 + 76*x^3 + 88*x^2 + x + 104, x^41 + 76*x^39 + 36*x^38 + 22*x^37 + 12*x^36 + 60*x^35 + 92*x^34 + 69*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 86*x^5 + 108*x^4 + 28*x^3 + 124*x^2 + 25*x + 84, x^41 + 76*x^39 + 124*x^38 + 70*x^37 + 36*x^36 + 92*x^35 + 36*x^34 + 117*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 6*x^5 + 68*x^4 + 60*x^3 + 4*x^2 + 73*x + 92, x^41 + 76*x^39 + 48*x^38 + 30*x^37 + 112*x^36 + 44*x^35 + 16*x^34 + 13*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 30*x^5 + 112*x^4 + 12*x^3 + 16*x^2 + 33*x + 80, x^41 + 76*x^39 + 112*x^38 + 110*x^37 + 64*x^36 + 76*x^35 + 48*x^34 + 29*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 110*x^5 + 64*x^4 + 44*x^3 + 48*x^2 + 49*x + 32, x^41 + 76*x^39 + 12*x^38 + 54*x^37 + 68*x^36 + 60*x^35 + 52*x^34 + 37*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 118*x^5 + 100*x^4 + 28*x^3 + 20*x^2 + 121*x + 28, x^41 + 76*x^39 + 72*x^38 + 110*x^37 + 40*x^36 + 76*x^35 + 88*x^34 + 29*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 110*x^5 + 104*x^4 + 44*x^3 + 24*x^2 + 49*x + 120, x^41 + 76*x^39 + 24*x^38 + 14*x^37 + 24*x^36 + 12*x^35 + 8*x^34 + 61*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 14*x^5 + 88*x^4 + 108*x^3 + 72*x^2 + 81*x + 8, x^41 + 76*x^39 + 64*x^38 + 46*x^37 + 112*x^36 + 76*x^35 + 96*x^34 + 93*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 46*x^5 + 112*x^4 + 44*x^3 + 96*x^2 + 113*x + 112, x^41 + 76*x^39 + 36*x^38 + 86*x^37 + 12*x^36 + 124*x^35 + 28*x^34 + 69*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 22*x^5 + 108*x^4 + 92*x^3 + 60*x^2 + 25*x + 20, x^41 + 76*x^39 + 96*x^38 + 78*x^37 + 112*x^36 + 76*x^35 + 64*x^34 + 61*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 78*x^5 + 112*x^4 + 44*x^3 + 64*x^2 + 81*x + 112, x^41 + 76*x^39 + 40*x^38 + 62*x^37 + 56*x^36 + 44*x^35 + 88*x^34 + 109*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 62*x^5 + 120*x^4 + 12*x^3 + 24*x^2 + x + 8, x^41 + 76*x^39 + 110*x^37 + 16*x^36 + 76*x^35 + 96*x^34 + 29*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 110*x^5 + 16*x^4 + 44*x^3 + 96*x^2 + 49*x + 16, x^41 + 76*x^39 + 92*x^38 + 118*x^37 + 84*x^36 + 124*x^35 + 100*x^34 + 37*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 54*x^5 + 116*x^4 + 92*x^3 + 68*x^2 + 121*x + 12, x^41 + 76*x^39 + 30*x^37 + 64*x^36 + 44*x^35 + 13*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 30*x^5 + 64*x^4 + 12*x^3 + 33*x + 64, x^41 + 76*x^39 + 48*x^38 + 14*x^37 + 32*x^36 + 12*x^35 + 48*x^34 + 61*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 14*x^5 + 32*x^4 + 108*x^3 + 48*x^2 + 81*x, x^41 + 76*x^39 + 40*x^38 + 14*x^37 + 104*x^36 + 12*x^35 + 56*x^34 + 61*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 14*x^5 + 40*x^4 + 108*x^3 + 120*x^2 + 81*x + 120, x^41 + 76*x^39 + 112*x^38 + 78*x^37 + 76*x^35 + 112*x^34 + 61*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 78*x^5 + 44*x^3 + 112*x^2 + 81*x + 32, x^41 + 76*x^39 + 68*x^38 + 22*x^37 + 44*x^36 + 124*x^35 + 124*x^34 + 5*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 86*x^5 + 12*x^4 + 92*x^3 + 28*x^2 + 89*x + 116, x^41 + 76*x^39 + 76*x^38 + 6*x^37 + 84*x^36 + 28*x^35 + 20*x^34 + 117*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 70*x^5 + 116*x^4 + 124*x^3 + 116*x^2 + 73*x + 108, x^41 + 76*x^39 + 4*x^38 + 70*x^37 + 92*x^36 + 92*x^35 + 92*x^34 + 117*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 6*x^5 + 60*x^4 + 60*x^3 + 124*x^2 + 73*x + 36, x^41 + 76*x^39 + 28*x^38 + 22*x^37 + 20*x^36 + 124*x^35 + 100*x^34 + 5*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 86*x^5 + 52*x^4 + 92*x^3 + 68*x^2 + 89*x + 12, x^41 + 76*x^39 + 60*x^38 + 6*x^37 + 100*x^36 + 92*x^35 + 100*x^34 + 53*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 70*x^5 + 4*x^4 + 60*x^3 + 68*x^2 + 9*x + 28, x^41 + 76*x^39 + 56*x^38 + 14*x^37 + 120*x^36 + 76*x^35 + 40*x^34 + 125*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 14*x^5 + 56*x^4 + 44*x^3 + 104*x^2 + 17*x + 104, x^41 + 76*x^39 + 56*x^38 + 30*x^37 + 104*x^36 + 44*x^35 + 8*x^34 + 13*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 30*x^5 + 40*x^4 + 12*x^3 + 72*x^2 + 33*x + 24, x^41 + 76*x^39 + 52*x^38 + 118*x^37 + 92*x^36 + 60*x^35 + 76*x^34 + 101*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 54*x^5 + 60*x^4 + 28*x^3 + 108*x^2 + 57*x + 4, x^41 + 76*x^39 + 32*x^38 + 14*x^37 + 16*x^36 + 76*x^35 + 64*x^34 + 125*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 14*x^5 + 16*x^4 + 44*x^3 + 64*x^2 + 17*x + 16, x^41 + 76*x^39 + 24*x^38 + 30*x^37 + 40*x^36 + 108*x^35 + 40*x^34 + 77*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 30*x^5 + 104*x^4 + 76*x^3 + 104*x^2 + 97*x + 88, x^41 + 76*x^39 + 94*x^37 + 96*x^36 + 108*x^35 + 13*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 94*x^5 + 96*x^4 + 76*x^3 + 33*x + 32, x^41 + 76*x^39 + 8*x^38 + 110*x^37 + 40*x^36 + 76*x^35 + 24*x^34 + 29*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 110*x^5 + 104*x^4 + 44*x^3 + 88*x^2 + 49*x + 120, x^41 + 76*x^39 + 8*x^38 + 126*x^37 + 24*x^36 + 44*x^35 + 120*x^34 + 45*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 126*x^5 + 88*x^4 + 12*x^3 + 56*x^2 + 65*x + 40, x^41 + 76*x^39 + 92*x^38 + 70*x^37 + 68*x^36 + 92*x^35 + 68*x^34 + 117*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 6*x^5 + 100*x^4 + 60*x^3 + 36*x^2 + 73*x + 60, x^41 + 76*x^39 + 32*x^38 + 62*x^37 + 64*x^36 + 108*x^35 + 32*x^34 + 45*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 62*x^5 + 64*x^4 + 76*x^3 + 32*x^2 + 65*x, x^41 + 76*x^39 + 12*x^38 + 22*x^37 + 4*x^36 + 124*x^35 + 52*x^34 + 5*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 86*x^5 + 36*x^4 + 92*x^3 + 20*x^2 + 89*x + 92, x^41 + 76*x^39 + 16*x^38 + 30*x^37 + 112*x^36 + 44*x^35 + 112*x^34 + 13*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 30*x^5 + 112*x^4 + 12*x^3 + 112*x^2 + 33*x + 16, x^41 + 76*x^39 + 40*x^38 + 110*x^37 + 40*x^36 + 76*x^35 + 56*x^34 + 29*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 110*x^5 + 104*x^4 + 44*x^3 + 120*x^2 + 49*x + 56, x^41 + 76*x^39 + 64*x^38 + 110*x^37 + 48*x^36 + 12*x^35 + 32*x^34 + 93*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 110*x^5 + 48*x^4 + 108*x^3 + 32*x^2 + 113*x + 112, x^41 + 76*x^39 + 88*x^38 + 110*x^37 + 24*x^36 + 76*x^35 + 72*x^34 + 29*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 110*x^5 + 88*x^4 + 44*x^3 + 8*x^2 + 49*x + 8, x^41 + 76*x^39 + 32*x^38 + 78*x^37 + 80*x^36 + 76*x^35 + 64*x^34 + 61*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 78*x^5 + 80*x^4 + 44*x^3 + 64*x^2 + 81*x + 80, x^41 + 76*x^39 + 4*x^38 + 102*x^37 + 92*x^36 + 92*x^35 + 28*x^34 + 85*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 38*x^5 + 60*x^4 + 60*x^3 + 60*x^2 + 41*x + 100, x^41 + 76*x^39 + 46*x^37 + 80*x^36 + 12*x^35 + 32*x^34 + 29*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 46*x^5 + 80*x^4 + 108*x^3 + 32*x^2 + 49*x + 16, x^41 + 76*x^39 + 48*x^38 + 78*x^37 + 32*x^36 + 76*x^35 + 112*x^34 + 61*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 78*x^5 + 32*x^4 + 44*x^3 + 112*x^2 + 81*x + 64, x^41 + 76*x^39 + 68*x^38 + 118*x^37 + 108*x^36 + 124*x^35 + 60*x^34 + 37*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 54*x^5 + 76*x^4 + 92*x^3 + 92*x^2 + 121*x + 116, x^41 + 76*x^39 + 20*x^38 + 6*x^37 + 76*x^36 + 92*x^35 + 76*x^34 + 53*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 70*x^5 + 44*x^4 + 60*x^3 + 108*x^2 + 9*x + 52, x^41 + 76*x^39 + 100*x^38 + 54*x^37 + 44*x^36 + 124*x^35 + 92*x^34 + 101*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 118*x^5 + 12*x^4 + 92*x^3 + 124*x^2 + 57*x + 116, x^41 + 76*x^39 + 16*x^38 + 78*x^37 + 32*x^36 + 12*x^35 + 16*x^34 + 125*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 78*x^5 + 32*x^4 + 108*x^3 + 16*x^2 + 17*x + 64, x^41 + 76*x^39 + 60*x^38 + 54*x^37 + 52*x^36 + 124*x^35 + 4*x^34 + 101*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 118*x^5 + 84*x^4 + 92*x^3 + 100*x^2 + 57*x + 44, x^41 + 76*x^39 + 120*x^38 + 78*x^37 + 24*x^36 + 76*x^35 + 40*x^34 + 61*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 78*x^5 + 88*x^4 + 44*x^3 + 104*x^2 + 81*x + 8, x^41 + 76*x^39 + 32*x^38 + 30*x^37 + 96*x^36 + 108*x^35 + 32*x^34 + 77*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 30*x^5 + 96*x^4 + 76*x^3 + 32*x^2 + 97*x + 96, x^41 + 76*x^39 + 44*x^38 + 118*x^37 + 100*x^36 + 124*x^35 + 84*x^34 + 37*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 54*x^5 + 4*x^4 + 92*x^3 + 52*x^2 + 121*x + 60, x^41 + 76*x^39 + 24*x^38 + 30*x^37 + 40*x^36 + 44*x^35 + 104*x^34 + 13*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 30*x^5 + 104*x^4 + 12*x^3 + 40*x^2 + 33*x + 24, x^41 + 76*x^39 + 24*x^38 + 14*x^37 + 88*x^36 + 76*x^35 + 72*x^34 + 125*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 14*x^5 + 24*x^4 + 44*x^3 + 8*x^2 + 17*x + 8, x^41 + 76*x^39 + 8*x^38 + 110*x^37 + 40*x^36 + 12*x^35 + 88*x^34 + 93*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 110*x^5 + 104*x^4 + 108*x^3 + 24*x^2 + 113*x + 56, x^41 + 76*x^39 + 56*x^38 + 94*x^37 + 72*x^36 + 108*x^35 + 8*x^34 + 13*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 94*x^5 + 8*x^4 + 76*x^3 + 72*x^2 + 33*x + 56, x^41 + 76*x^39 + 96*x^38 + 46*x^37 + 16*x^36 + 76*x^35 + 64*x^34 + 93*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 46*x^5 + 16*x^4 + 44*x^3 + 64*x^2 + 113*x + 80, x^41 + 76*x^39 + 124*x^38 + 118*x^37 + 52*x^36 + 124*x^35 + 68*x^34 + 37*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 54*x^5 + 84*x^4 + 92*x^3 + 36*x^2 + 121*x + 44, x^41 + 76*x^39 + 96*x^38 + 30*x^37 + 108*x^35 + 32*x^34 + 77*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 30*x^5 + 76*x^3 + 32*x^2 + 97*x, x^41 + 76*x^39 + 56*x^38 + 110*x^37 + 56*x^36 + 76*x^35 + 104*x^34 + 29*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 110*x^5 + 120*x^4 + 44*x^3 + 40*x^2 + 49*x + 104, x^41 + 76*x^39 + 112*x^38 + 78*x^37 + 64*x^36 + 76*x^35 + 112*x^34 + 61*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 78*x^5 + 64*x^4 + 44*x^3 + 112*x^2 + 81*x + 96, x^41 + 76*x^39 + 104*x^38 + 126*x^37 + 88*x^36 + 44*x^35 + 88*x^34 + 45*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 126*x^5 + 24*x^4 + 12*x^3 + 24*x^2 + 65*x + 40, x^41 + 76*x^39 + 72*x^38 + 126*x^37 + 56*x^36 + 108*x^35 + 56*x^34 + 109*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 126*x^5 + 120*x^4 + 76*x^3 + 120*x^2 + x + 8, x^41 + 76*x^39 + 60*x^38 + 102*x^37 + 36*x^36 + 92*x^35 + 36*x^34 + 85*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 38*x^5 + 68*x^4 + 60*x^3 + 4*x^2 + 41*x + 28, x^41 + 76*x^39 + 32*x^38 + 30*x^37 + 64*x^36 + 44*x^35 + 32*x^34 + 13*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 30*x^5 + 64*x^4 + 12*x^3 + 32*x^2 + 33*x, x^41 + 76*x^39 + 8*x^38 + 46*x^37 + 8*x^36 + 76*x^35 + 88*x^34 + 93*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 46*x^5 + 72*x^4 + 44*x^3 + 24*x^2 + 113*x + 88, x^41 + 76*x^39 + 80*x^38 + 126*x^37 + 48*x^36 + 108*x^35 + 48*x^34 + 109*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 126*x^5 + 48*x^4 + 76*x^3 + 48*x^2 + x + 80, x^41 + 76*x^39 + 64*x^38 + 14*x^37 + 48*x^36 + 76*x^35 + 32*x^34 + 125*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 14*x^5 + 48*x^4 + 44*x^3 + 32*x^2 + 17*x + 112, x^41 + 76*x^39 + 116*x^38 + 86*x^37 + 60*x^36 + 124*x^35 + 76*x^34 + 69*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 22*x^5 + 28*x^4 + 92*x^3 + 108*x^2 + 25*x + 100, x^41 + 76*x^39 + 64*x^38 + 110*x^37 + 112*x^36 + 12*x^35 + 32*x^34 + 93*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 110*x^5 + 112*x^4 + 108*x^3 + 32*x^2 + 113*x + 48, x^41 + 76*x^39 + 64*x^38 + 126*x^37 + 96*x^36 + 108*x^35 + 109*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 126*x^5 + 96*x^4 + 76*x^3 + x + 96, x^41 + 76*x^39 + 96*x^38 + 46*x^37 + 48*x^36 + 12*x^35 + 64*x^34 + 29*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 46*x^5 + 48*x^4 + 108*x^3 + 64*x^2 + 49*x + 48, x^41 + 76*x^39 + 88*x^38 + 46*x^37 + 56*x^36 + 76*x^35 + 8*x^34 + 93*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 46*x^5 + 120*x^4 + 44*x^3 + 72*x^2 + 113*x + 40, x^41 + 76*x^39 + 60*x^38 + 86*x^37 + 20*x^36 + 124*x^35 + 4*x^34 + 69*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 22*x^5 + 52*x^4 + 92*x^3 + 100*x^2 + 25*x + 76, x^41 + 76*x^39 + 126*x^37 + 64*x^36 + 108*x^35 + 109*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 126*x^5 + 64*x^4 + 76*x^3 + x + 64, x^41 + 76*x^39 + 112*x^38 + 14*x^37 + 96*x^36 + 76*x^35 + 48*x^34 + 125*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 14*x^5 + 96*x^4 + 44*x^3 + 48*x^2 + 17*x, x^41 + 76*x^39 + 100*x^38 + 118*x^37 + 108*x^36 + 60*x^35 + 28*x^34 + 101*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 54*x^5 + 76*x^4 + 28*x^3 + 60*x^2 + 57*x + 116, x^41 + 76*x^39 + 76*x^38 + 70*x^37 + 116*x^36 + 92*x^35 + 20*x^34 + 117*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 6*x^5 + 20*x^4 + 60*x^3 + 116*x^2 + 73*x + 76, x^41 + 76*x^39 + 76*x^38 + 118*x^37 + 4*x^36 + 60*x^35 + 116*x^34 + 101*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 54*x^5 + 36*x^4 + 28*x^3 + 84*x^2 + 57*x + 92, x^41 + 76*x^39 + 72*x^38 + 94*x^37 + 120*x^36 + 44*x^35 + 56*x^34 + 77*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 94*x^5 + 56*x^4 + 12*x^3 + 120*x^2 + 97*x + 72, x^41 + 76*x^39 + 96*x^38 + 62*x^37 + 108*x^35 + 96*x^34 + 45*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 62*x^5 + 76*x^3 + 96*x^2 + 65*x + 64, x^41 + 76*x^39 + 120*x^38 + 126*x^37 + 104*x^36 + 108*x^35 + 72*x^34 + 109*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 126*x^5 + 40*x^4 + 76*x^3 + 8*x^2 + x + 24, x^41 + 76*x^39 + 36*x^38 + 70*x^37 + 92*x^36 + 92*x^35 + 124*x^34 + 117*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 6*x^5 + 60*x^4 + 60*x^3 + 28*x^2 + 73*x + 100, x^41 + 76*x^39 + 40*x^38 + 14*x^37 + 8*x^36 + 76*x^35 + 56*x^34 + 125*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 14*x^5 + 72*x^4 + 44*x^3 + 120*x^2 + 17*x + 88, x^41 + 76*x^39 + 36*x^38 + 6*x^37 + 92*x^36 + 92*x^35 + 124*x^34 + 53*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 70*x^5 + 60*x^4 + 60*x^3 + 28*x^2 + 9*x + 100, x^41 + 76*x^39 + 32*x^38 + 14*x^37 + 48*x^36 + 76*x^35 + 125*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 14*x^5 + 48*x^4 + 44*x^3 + 17*x + 48, x^41 + 76*x^39 + 68*x^38 + 22*x^37 + 76*x^36 + 60*x^35 + 124*x^34 + 69*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 86*x^5 + 44*x^4 + 28*x^3 + 28*x^2 + 25*x + 84, x^41 + 76*x^39 + 40*x^38 + 94*x^37 + 56*x^36 + 108*x^35 + 88*x^34 + 13*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 94*x^5 + 120*x^4 + 76*x^3 + 24*x^2 + 33*x + 8, x^41 + 76*x^39 + 44*x^38 + 118*x^37 + 100*x^36 + 60*x^35 + 20*x^34 + 101*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 54*x^5 + 4*x^4 + 28*x^3 + 116*x^2 + 57*x + 124, x^41 + 76*x^39 + 112*x^38 + 94*x^37 + 112*x^36 + 108*x^35 + 16*x^34 + 13*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 94*x^5 + 112*x^4 + 76*x^3 + 16*x^2 + 33*x + 16, x^41 + 76*x^39 + 88*x^38 + 14*x^37 + 120*x^36 + 12*x^35 + 8*x^34 + 61*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 14*x^5 + 56*x^4 + 108*x^3 + 72*x^2 + 81*x + 104, x^41 + 76*x^39 + 36*x^38 + 38*x^37 + 92*x^36 + 28*x^35 + 124*x^34 + 85*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 102*x^5 + 60*x^4 + 124*x^3 + 28*x^2 + 41*x + 100, x^41 + 76*x^39 + 56*x^38 + 110*x^37 + 24*x^36 + 76*x^35 + 40*x^34 + 29*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 110*x^5 + 88*x^4 + 44*x^3 + 104*x^2 + 49*x + 72, x^41 + 76*x^39 + 52*x^38 + 22*x^37 + 124*x^36 + 124*x^35 + 12*x^34 + 5*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 86*x^5 + 92*x^4 + 92*x^3 + 44*x^2 + 89*x + 36, x^41 + 76*x^39 + 64*x^38 + 78*x^37 + 112*x^36 + 12*x^35 + 96*x^34 + 125*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 78*x^5 + 112*x^4 + 108*x^3 + 96*x^2 + 17*x + 112, x^41 + 76*x^39 + 52*x^38 + 102*x^37 + 12*x^36 + 92*x^35 + 44*x^34 + 85*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 38*x^5 + 108*x^4 + 60*x^3 + 76*x^2 + 41*x + 116, x^41 + 76*x^39 + 16*x^38 + 46*x^37 + 32*x^36 + 76*x^35 + 16*x^34 + 93*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 46*x^5 + 32*x^4 + 44*x^3 + 16*x^2 + 113*x + 64, x^41 + 76*x^39 + 32*x^38 + 126*x^37 + 32*x^36 + 108*x^35 + 96*x^34 + 109*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 126*x^5 + 32*x^4 + 76*x^3 + 96*x^2 + x + 96, x^41 + 76*x^39 + 16*x^38 + 78*x^37 + 76*x^35 + 16*x^34 + 61*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 78*x^5 + 44*x^3 + 16*x^2 + 81*x + 96, x^41 + 76*x^39 + 20*x^38 + 6*x^37 + 76*x^36 + 28*x^35 + 12*x^34 + 117*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 70*x^5 + 44*x^4 + 124*x^3 + 44*x^2 + 73*x + 116, x^41 + 76*x^39 + 16*x^38 + 78*x^37 + 96*x^36 + 76*x^35 + 80*x^34 + 61*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 78*x^5 + 96*x^4 + 44*x^3 + 80*x^2 + 81*x + 64, x^41 + 76*x^39 + 120*x^38 + 94*x^37 + 40*x^36 + 44*x^35 + 72*x^34 + 77*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 94*x^5 + 104*x^4 + 12*x^3 + 8*x^2 + 97*x + 88, x^41 + 76*x^39 + 92*x^38 + 54*x^37 + 116*x^36 + 60*x^35 + 100*x^34 + 37*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 118*x^5 + 20*x^4 + 28*x^3 + 68*x^2 + 121*x + 108, x^41 + 76*x^39 + 96*x^38 + 62*x^37 + 44*x^35 + 32*x^34 + 109*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 62*x^5 + 12*x^3 + 32*x^2 + x, x^41 + 76*x^39 + 100*x^38 + 6*x^37 + 124*x^36 + 28*x^35 + 60*x^34 + 117*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 70*x^5 + 92*x^4 + 124*x^3 + 92*x^2 + 73*x + 68, x^41 + 76*x^39 + 96*x^38 + 30*x^37 + 44*x^35 + 96*x^34 + 13*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 30*x^5 + 12*x^3 + 96*x^2 + 33*x + 64, x^41 + 76*x^39 + 104*x^38 + 46*x^37 + 72*x^36 + 76*x^35 + 56*x^34 + 93*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 46*x^5 + 8*x^4 + 44*x^3 + 120*x^2 + 113*x + 88, x^41 + 76*x^39 + 24*x^38 + 110*x^37 + 24*x^36 + 12*x^35 + 72*x^34 + 93*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 110*x^5 + 88*x^4 + 108*x^3 + 8*x^2 + 113*x + 72, x^41 + 76*x^39 + 40*x^38 + 78*x^37 + 104*x^36 + 12*x^35 + 56*x^34 + 125*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 78*x^5 + 40*x^4 + 108*x^3 + 120*x^2 + 17*x + 120, x^41 + 76*x^39 + 32*x^38 + 110*x^37 + 16*x^36 + 12*x^35 + 64*x^34 + 93*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 110*x^5 + 16*x^4 + 108*x^3 + 64*x^2 + 113*x + 16, x^41 + 76*x^39 + 88*x^38 + 110*x^37 + 24*x^36 + 12*x^35 + 8*x^34 + 93*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 110*x^5 + 88*x^4 + 108*x^3 + 72*x^2 + 113*x + 72, x^41 + 76*x^39 + 124*x^38 + 22*x^37 + 116*x^36 + 124*x^35 + 4*x^34 + 5*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 86*x^5 + 20*x^4 + 92*x^3 + 100*x^2 + 89*x + 44, x^41 + 76*x^39 + 96*x^38 + 46*x^37 + 48*x^36 + 76*x^35 + 93*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 46*x^5 + 48*x^4 + 44*x^3 + 113*x + 112, x^41 + 76*x^39 + 112*x^38 + 46*x^37 + 64*x^36 + 76*x^35 + 48*x^34 + 93*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 46*x^5 + 64*x^4 + 44*x^3 + 48*x^2 + 113*x + 32, x^41 + 76*x^39 + 40*x^38 + 94*x^37 + 88*x^36 + 44*x^35 + 88*x^34 + 77*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 94*x^5 + 24*x^4 + 12*x^3 + 24*x^2 + 97*x + 104, x^41 + 76*x^39 + 76*x^38 + 54*x^37 + 4*x^36 + 60*x^35 + 116*x^34 + 37*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 118*x^5 + 36*x^4 + 28*x^3 + 84*x^2 + 121*x + 92, x^41 + 76*x^39 + 16*x^38 + 126*x^37 + 80*x^36 + 108*x^35 + 48*x^34 + 109*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 126*x^5 + 80*x^4 + 76*x^3 + 48*x^2 + x + 112, x^41 + 76*x^39 + 32*x^38 + 126*x^37 + 64*x^36 + 108*x^35 + 32*x^34 + 109*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 126*x^5 + 64*x^4 + 76*x^3 + 32*x^2 + x, x^41 + 76*x^39 + 112*x^38 + 62*x^37 + 16*x^36 + 108*x^35 + 16*x^34 + 45*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 62*x^5 + 16*x^4 + 76*x^3 + 16*x^2 + 65*x + 112, x^41 + 76*x^39 + 12*x^38 + 86*x^37 + 100*x^36 + 124*x^35 + 116*x^34 + 69*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 22*x^5 + 4*x^4 + 92*x^3 + 84*x^2 + 25*x + 60, x^41 + 76*x^39 + 44*x^38 + 22*x^37 + 4*x^36 + 124*x^35 + 84*x^34 + 5*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 86*x^5 + 36*x^4 + 92*x^3 + 52*x^2 + 89*x + 28, x^41 + 76*x^39 + 64*x^38 + 30*x^37 + 32*x^36 + 44*x^35 + 13*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 30*x^5 + 32*x^4 + 12*x^3 + 33*x + 32, x^41 + 76*x^39 + 124*x^38 + 102*x^37 + 100*x^36 + 92*x^35 + 100*x^34 + 85*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 38*x^5 + 4*x^4 + 60*x^3 + 68*x^2 + 41*x + 92, x^41 + 76*x^39 + 116*x^38 + 54*x^37 + 60*x^36 + 124*x^35 + 12*x^34 + 101*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 118*x^5 + 28*x^4 + 92*x^3 + 44*x^2 + 57*x + 36, x^41 + 76*x^39 + 36*x^38 + 102*x^37 + 92*x^36 + 92*x^35 + 60*x^34 + 85*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 38*x^5 + 60*x^4 + 60*x^3 + 92*x^2 + 41*x + 36, x^41 + 76*x^39 + 100*x^38 + 118*x^37 + 12*x^36 + 124*x^35 + 28*x^34 + 37*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 54*x^5 + 108*x^4 + 92*x^3 + 60*x^2 + 121*x + 84, x^41 + 76*x^39 + 20*x^38 + 38*x^37 + 108*x^36 + 28*x^35 + 12*x^34 + 85*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 102*x^5 + 76*x^4 + 124*x^3 + 44*x^2 + 41*x + 84, x^41 + 76*x^39 + 108*x^38 + 102*x^37 + 52*x^36 + 92*x^35 + 116*x^34 + 85*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 38*x^5 + 84*x^4 + 60*x^3 + 84*x^2 + 41*x + 12, x^41 + 76*x^39 + 14*x^37 + 16*x^36 + 76*x^35 + 32*x^34 + 125*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 14*x^5 + 16*x^4 + 44*x^3 + 32*x^2 + 17*x + 80, x^41 + 76*x^39 + 104*x^38 + 110*x^37 + 72*x^36 + 76*x^35 + 56*x^34 + 29*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 110*x^5 + 8*x^4 + 44*x^3 + 120*x^2 + 49*x + 88, x^41 + 76*x^39 + 20*x^38 + 70*x^37 + 76*x^36 + 28*x^35 + 12*x^34 + 53*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 6*x^5 + 44*x^4 + 124*x^3 + 44*x^2 + 9*x + 116, x^41 + 76*x^39 + 80*x^38 + 46*x^37 + 32*x^36 + 76*x^35 + 80*x^34 + 93*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 46*x^5 + 32*x^4 + 44*x^3 + 80*x^2 + 113*x + 64, x^41 + 76*x^39 + 76*x^38 + 6*x^37 + 116*x^36 + 28*x^35 + 84*x^34 + 117*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 70*x^5 + 20*x^4 + 124*x^3 + 52*x^2 + 73*x + 12, x^41 + 76*x^39 + 120*x^38 + 94*x^37 + 8*x^36 + 44*x^35 + 8*x^34 + 77*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 94*x^5 + 72*x^4 + 12*x^3 + 72*x^2 + 97*x + 56, x^41 + 76*x^39 + 112*x^38 + 94*x^37 + 80*x^36 + 108*x^35 + 80*x^34 + 13*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 94*x^5 + 80*x^4 + 76*x^3 + 80*x^2 + 33*x + 112, x^41 + 76*x^39 + 24*x^38 + 14*x^37 + 56*x^36 + 76*x^35 + 8*x^34 + 125*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 14*x^5 + 120*x^4 + 44*x^3 + 72*x^2 + 17*x + 104, x^41 + 76*x^39 + 108*x^38 + 54*x^37 + 100*x^36 + 124*x^35 + 20*x^34 + 101*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 118*x^5 + 4*x^4 + 92*x^3 + 116*x^2 + 57*x + 60, x^41 + 76*x^39 + 40*x^38 + 110*x^37 + 8*x^36 + 76*x^35 + 120*x^34 + 29*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 110*x^5 + 72*x^4 + 44*x^3 + 56*x^2 + 49*x + 24, x^41 + 76*x^39 + 52*x^38 + 54*x^37 + 92*x^36 + 60*x^35 + 76*x^34 + 37*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 118*x^5 + 60*x^4 + 28*x^3 + 108*x^2 + 121*x + 4, x^41 + 76*x^39 + 96*x^38 + 78*x^37 + 16*x^36 + 12*x^35 + 64*x^34 + 125*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 78*x^5 + 16*x^4 + 108*x^3 + 64*x^2 + 17*x + 80, x^41 + 76*x^39 + 100*x^38 + 22*x^37 + 44*x^36 + 124*x^35 + 28*x^34 + 5*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 86*x^5 + 12*x^4 + 92*x^3 + 60*x^2 + 89*x + 52, x^41 + 76*x^39 + 116*x^38 + 38*x^37 + 76*x^36 + 28*x^35 + 44*x^34 + 85*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 102*x^5 + 44*x^4 + 124*x^3 + 76*x^2 + 41*x + 116, x^41 + 76*x^39 + 44*x^38 + 22*x^37 + 68*x^36 + 124*x^35 + 84*x^34 + 5*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 86*x^5 + 100*x^4 + 92*x^3 + 52*x^2 + 89*x + 92, x^41 + 76*x^39 + 88*x^38 + 94*x^37 + 72*x^36 + 108*x^35 + 40*x^34 + 13*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 94*x^5 + 8*x^4 + 76*x^3 + 104*x^2 + 33*x + 120, x^41 + 76*x^39 + 96*x^38 + 46*x^37 + 112*x^36 + 76*x^35 + 93*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 46*x^5 + 112*x^4 + 44*x^3 + 113*x + 48, x^41 + 76*x^39 + 84*x^38 + 118*x^37 + 60*x^36 + 124*x^35 + 108*x^34 + 37*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 54*x^5 + 28*x^4 + 92*x^3 + 12*x^2 + 121*x + 100, x^41 + 76*x^39 + 36*x^38 + 118*x^37 + 76*x^36 + 124*x^35 + 92*x^34 + 37*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 54*x^5 + 44*x^4 + 92*x^3 + 124*x^2 + 121*x + 20, x^41 + 76*x^39 + 28*x^38 + 102*x^37 + 4*x^36 + 28*x^35 + 4*x^34 + 21*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 38*x^5 + 36*x^4 + 124*x^3 + 100*x^2 + 105*x + 124, x^41 + 76*x^39 + 40*x^38 + 110*x^37 + 40*x^36 + 12*x^35 + 120*x^34 + 93*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 110*x^5 + 104*x^4 + 108*x^3 + 56*x^2 + 113*x + 120, x^41 + 76*x^39 + 76*x^38 + 22*x^37 + 36*x^36 + 60*x^35 + 116*x^34 + 69*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 86*x^5 + 68*x^4 + 28*x^3 + 84*x^2 + 25*x + 60, x^41 + 76*x^39 + 112*x^38 + 94*x^37 + 112*x^36 + 44*x^35 + 80*x^34 + 77*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 94*x^5 + 112*x^4 + 12*x^3 + 80*x^2 + 97*x + 80, x^41 + 76*x^39 + 16*x^38 + 46*x^37 + 64*x^36 + 76*x^35 + 80*x^34 + 93*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 46*x^5 + 64*x^4 + 44*x^3 + 80*x^2 + 113*x + 96, x^41 + 76*x^39 + 100*x^38 + 6*x^37 + 92*x^36 + 92*x^35 + 60*x^34 + 53*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 70*x^5 + 60*x^4 + 60*x^3 + 92*x^2 + 9*x + 100, x^41 + 76*x^39 + 88*x^38 + 14*x^37 + 88*x^36 + 76*x^35 + 8*x^34 + 125*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 14*x^5 + 24*x^4 + 44*x^3 + 72*x^2 + 17*x + 8, x^41 + 76*x^39 + 110*x^37 + 80*x^36 + 76*x^35 + 96*x^34 + 29*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 110*x^5 + 80*x^4 + 44*x^3 + 96*x^2 + 49*x + 80, x^41 + 76*x^39 + 108*x^38 + 102*x^37 + 116*x^36 + 28*x^35 + 52*x^34 + 21*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 38*x^5 + 20*x^4 + 124*x^3 + 20*x^2 + 105*x + 12, x^41 + 76*x^39 + 40*x^38 + 46*x^37 + 40*x^36 + 12*x^35 + 120*x^34 + 29*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 46*x^5 + 104*x^4 + 108*x^3 + 56*x^2 + 49*x + 120, x^41 + 76*x^39 + 48*x^38 + 110*x^37 + 96*x^36 + 12*x^35 + 112*x^34 + 93*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 110*x^5 + 96*x^4 + 108*x^3 + 112*x^2 + 113*x, x^41 + 76*x^39 + 16*x^38 + 110*x^37 + 76*x^35 + 80*x^34 + 29*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 110*x^5 + 44*x^3 + 80*x^2 + 49*x + 32, x^41 + 76*x^39 + 8*x^38 + 94*x^37 + 120*x^36 + 44*x^35 + 120*x^34 + 77*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 94*x^5 + 56*x^4 + 12*x^3 + 56*x^2 + 97*x + 72, x^41 + 76*x^39 + 88*x^38 + 94*x^37 + 72*x^36 + 44*x^35 + 104*x^34 + 77*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 94*x^5 + 8*x^4 + 12*x^3 + 40*x^2 + 97*x + 56, x^41 + 76*x^39 + 60*x^38 + 118*x^37 + 52*x^36 + 124*x^35 + 4*x^34 + 37*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 54*x^5 + 84*x^4 + 92*x^3 + 100*x^2 + 121*x + 44, x^41 + 76*x^39 + 80*x^38 + 126*x^37 + 16*x^36 + 44*x^35 + 48*x^34 + 45*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 126*x^5 + 16*x^4 + 12*x^3 + 48*x^2 + 65*x + 112, x^41 + 76*x^39 + 60*x^38 + 38*x^37 + 36*x^36 + 28*x^35 + 100*x^34 + 85*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 102*x^5 + 68*x^4 + 124*x^3 + 68*x^2 + 41*x + 92, x^41 + 76*x^39 + 4*x^38 + 38*x^37 + 92*x^36 + 92*x^35 + 28*x^34 + 21*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 102*x^5 + 60*x^4 + 60*x^3 + 60*x^2 + 105*x + 100, x^41 + 76*x^39 + 96*x^38 + 126*x^37 + 108*x^35 + 96*x^34 + 109*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 126*x^5 + 76*x^3 + 96*x^2 + x + 64, x^41 + 76*x^39 + 52*x^38 + 22*x^37 + 92*x^36 + 60*x^35 + 12*x^34 + 69*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 86*x^5 + 60*x^4 + 28*x^3 + 44*x^2 + 25*x + 68, x^41 + 76*x^39 + 16*x^38 + 78*x^37 + 64*x^36 + 12*x^35 + 80*x^34 + 125*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 78*x^5 + 64*x^4 + 108*x^3 + 80*x^2 + 17*x + 96, x^41 + 76*x^39 + 56*x^38 + 94*x^37 + 8*x^36 + 44*x^35 + 72*x^34 + 77*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 94*x^5 + 72*x^4 + 12*x^3 + 8*x^2 + 97*x + 56, x^41 + 76*x^39 + 96*x^38 + 78*x^37 + 80*x^36 + 12*x^35 + 64*x^34 + 125*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 78*x^5 + 80*x^4 + 108*x^3 + 64*x^2 + 17*x + 16, x^41 + 76*x^39 + 124*x^38 + 22*x^37 + 52*x^36 + 124*x^35 + 4*x^34 + 5*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 86*x^5 + 84*x^4 + 92*x^3 + 100*x^2 + 89*x + 108, x^41 + 76*x^39 + 68*x^38 + 70*x^37 + 60*x^36 + 92*x^35 + 92*x^34 + 117*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 6*x^5 + 28*x^4 + 60*x^3 + 124*x^2 + 73*x + 4, x^41 + 76*x^39 + 88*x^38 + 110*x^37 + 120*x^36 + 76*x^35 + 8*x^34 + 29*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 110*x^5 + 56*x^4 + 44*x^3 + 72*x^2 + 49*x + 104, x^41 + 76*x^39 + 32*x^38 + 46*x^37 + 112*x^36 + 12*x^35 + 29*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 46*x^5 + 112*x^4 + 108*x^3 + 49*x + 112, x^41 + 76*x^39 + 116*x^38 + 6*x^37 + 44*x^36 + 28*x^35 + 44*x^34 + 117*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 70*x^5 + 12*x^4 + 124*x^3 + 76*x^2 + 73*x + 20, x^41 + 76*x^39 + 56*x^38 + 30*x^37 + 8*x^36 + 44*x^35 + 72*x^34 + 13*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 30*x^5 + 72*x^4 + 12*x^3 + 8*x^2 + 33*x + 56, x^41 + 76*x^39 + 44*x^38 + 118*x^37 + 68*x^36 + 124*x^35 + 20*x^34 + 37*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 54*x^5 + 100*x^4 + 92*x^3 + 116*x^2 + 121*x + 28, x^41 + 76*x^39 + 44*x^38 + 22*x^37 + 36*x^36 + 124*x^35 + 20*x^34 + 5*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 86*x^5 + 68*x^4 + 92*x^3 + 116*x^2 + 89*x + 60, x^41 + 76*x^39 + 80*x^38 + 30*x^37 + 16*x^36 + 44*x^35 + 112*x^34 + 13*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 30*x^5 + 16*x^4 + 12*x^3 + 112*x^2 + 33*x + 48, x^41 + 76*x^39 + 112*x^38 + 126*x^37 + 80*x^36 + 108*x^35 + 16*x^34 + 109*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 126*x^5 + 80*x^4 + 76*x^3 + 16*x^2 + x + 48, x^41 + 76*x^39 + 4*x^38 + 102*x^37 + 28*x^36 + 92*x^35 + 28*x^34 + 85*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 38*x^5 + 124*x^4 + 60*x^3 + 60*x^2 + 41*x + 36, x^41 + 76*x^39 + 52*x^38 + 102*x^37 + 44*x^36 + 92*x^35 + 108*x^34 + 85*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 38*x^5 + 12*x^4 + 60*x^3 + 12*x^2 + 41*x + 20, x^41 + 76*x^39 + 46*x^37 + 16*x^36 + 76*x^35 + 96*x^34 + 93*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 46*x^5 + 16*x^4 + 44*x^3 + 96*x^2 + 113*x + 16, x^41 + 76*x^39 + 28*x^38 + 22*x^37 + 20*x^36 + 60*x^35 + 36*x^34 + 69*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 86*x^5 + 52*x^4 + 28*x^3 + 4*x^2 + 25*x + 76, x^41 + 76*x^39 + 100*x^38 + 22*x^37 + 12*x^36 + 60*x^35 + 28*x^34 + 69*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 86*x^5 + 108*x^4 + 28*x^3 + 60*x^2 + 25*x + 84, x^41 + 76*x^39 + 12*x^38 + 102*x^37 + 116*x^36 + 28*x^35 + 84*x^34 + 21*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 38*x^5 + 20*x^4 + 124*x^3 + 52*x^2 + 105*x + 76, x^41 + 76*x^39 + 112*x^38 + 14*x^37 + 32*x^36 + 12*x^35 + 112*x^34 + 61*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 14*x^5 + 32*x^4 + 108*x^3 + 112*x^2 + 81*x, x^41 + 76*x^39 + 28*x^38 + 118*x^37 + 52*x^36 + 124*x^35 + 100*x^34 + 37*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 54*x^5 + 84*x^4 + 92*x^3 + 68*x^2 + 121*x + 108, x^41 + 76*x^39 + 84*x^38 + 54*x^37 + 124*x^36 + 60*x^35 + 44*x^34 + 37*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 118*x^5 + 92*x^4 + 28*x^3 + 76*x^2 + 121*x + 100, x^41 + 76*x^39 + 4*x^38 + 54*x^37 + 44*x^36 + 124*x^35 + 124*x^34 + 101*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 118*x^5 + 12*x^4 + 92*x^3 + 28*x^2 + 57*x + 52, x^41 + 76*x^39 + 48*x^38 + 110*x^37 + 96*x^36 + 76*x^35 + 48*x^34 + 29*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 110*x^5 + 96*x^4 + 44*x^3 + 48*x^2 + 49*x + 64, x^41 + 76*x^39 + 124*x^38 + 54*x^37 + 20*x^36 + 124*x^35 + 4*x^34 + 101*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 118*x^5 + 52*x^4 + 92*x^3 + 100*x^2 + 57*x + 12, x^41 + 76*x^39 + 32*x^38 + 126*x^37 + 44*x^35 + 96*x^34 + 45*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 126*x^5 + 12*x^3 + 96*x^2 + 65*x, x^41 + 76*x^39 + 92*x^38 + 54*x^37 + 116*x^36 + 124*x^35 + 36*x^34 + 101*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 118*x^5 + 20*x^4 + 92*x^3 + 4*x^2 + 57*x + 44, x^41 + 76*x^39 + 52*x^38 + 54*x^37 + 60*x^36 + 60*x^35 + 12*x^34 + 37*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 118*x^5 + 28*x^4 + 28*x^3 + 44*x^2 + 121*x + 100, x^41 + 76*x^39 + 28*x^38 + 38*x^37 + 36*x^36 + 92*x^35 + 4*x^34 + 21*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 102*x^5 + 68*x^4 + 60*x^3 + 100*x^2 + 105*x + 92, x^41 + 76*x^39 + 64*x^38 + 30*x^37 + 32*x^36 + 108*x^35 + 64*x^34 + 77*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 30*x^5 + 32*x^4 + 76*x^3 + 64*x^2 + 97*x + 96, x^41 + 76*x^39 + 72*x^38 + 78*x^37 + 8*x^36 + 12*x^35 + 24*x^34 + 125*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 78*x^5 + 72*x^4 + 108*x^3 + 88*x^2 + 17*x + 88, x^41 + 76*x^39 + 108*x^38 + 86*x^37 + 36*x^36 + 124*x^35 + 84*x^34 + 69*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 22*x^5 + 68*x^4 + 92*x^3 + 52*x^2 + 25*x + 60, x^41 + 76*x^39 + 88*x^38 + 126*x^37 + 40*x^36 + 44*x^35 + 104*x^34 + 45*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 126*x^5 + 104*x^4 + 12*x^3 + 40*x^2 + 65*x + 88, x^41 + 76*x^39 + 80*x^38 + 14*x^37 + 32*x^36 + 76*x^35 + 16*x^34 + 125*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 14*x^5 + 32*x^4 + 44*x^3 + 16*x^2 + 17*x, x^41 + 76*x^39 + 96*x^38 + 78*x^37 + 48*x^36 + 12*x^35 + 125*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 78*x^5 + 48*x^4 + 108*x^3 + 17*x + 112, x^41 + 76*x^39 + 44*x^38 + 70*x^37 + 84*x^36 + 28*x^35 + 116*x^34 + 53*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 6*x^5 + 116*x^4 + 124*x^3 + 84*x^2 + 9*x + 44, x^41 + 76*x^39 + 16*x^38 + 110*x^37 + 64*x^36 + 76*x^35 + 80*x^34 + 29*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 110*x^5 + 64*x^4 + 44*x^3 + 80*x^2 + 49*x + 96, x^41 + 76*x^39 + 32*x^38 + 110*x^37 + 80*x^36 + 76*x^35 + 29*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 110*x^5 + 80*x^4 + 44*x^3 + 49*x + 16, x^41 + 76*x^39 + 68*x^38 + 54*x^37 + 12*x^36 + 60*x^35 + 60*x^34 + 37*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 118*x^5 + 108*x^4 + 28*x^3 + 92*x^2 + 121*x + 84, x^41 + 76*x^39 + 108*x^38 + 54*x^37 + 36*x^36 + 124*x^35 + 20*x^34 + 101*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 118*x^5 + 68*x^4 + 92*x^3 + 116*x^2 + 57*x + 124, x^41 + 76*x^39 + 48*x^38 + 30*x^37 + 48*x^36 + 44*x^35 + 16*x^34 + 13*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 30*x^5 + 48*x^4 + 12*x^3 + 16*x^2 + 33*x + 16, x^41 + 76*x^39 + 60*x^38 + 6*x^37 + 68*x^36 + 28*x^35 + 100*x^34 + 117*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 70*x^5 + 100*x^4 + 124*x^3 + 68*x^2 + 73*x + 60, x^41 + 76*x^39 + 100*x^38 + 86*x^37 + 76*x^36 + 60*x^35 + 28*x^34 + 5*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 22*x^5 + 44*x^4 + 28*x^3 + 60*x^2 + 89*x + 20, x^41 + 76*x^39 + 48*x^38 + 126*x^37 + 48*x^36 + 108*x^35 + 16*x^34 + 109*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 126*x^5 + 48*x^4 + 76*x^3 + 16*x^2 + x + 16, x^41 + 76*x^39 + 72*x^38 + 62*x^37 + 88*x^36 + 44*x^35 + 56*x^34 + 109*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 62*x^5 + 24*x^4 + 12*x^3 + 120*x^2 + x + 104, x^41 + 76*x^39 + 100*x^38 + 38*x^37 + 28*x^36 + 92*x^35 + 124*x^34 + 21*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 102*x^5 + 124*x^4 + 60*x^3 + 28*x^2 + 105*x + 100, x^41 + 76*x^39 + 100*x^38 + 22*x^37 + 108*x^36 + 60*x^35 + 92*x^34 + 69*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 86*x^5 + 76*x^4 + 28*x^3 + 124*x^2 + 25*x + 52, x^41 + 76*x^39 + 100*x^38 + 38*x^37 + 124*x^36 + 28*x^35 + 124*x^34 + 85*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 102*x^5 + 92*x^4 + 124*x^3 + 28*x^2 + 41*x + 4, x^41 + 76*x^39 + 96*x^38 + 46*x^37 + 112*x^36 + 12*x^35 + 64*x^34 + 29*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 46*x^5 + 112*x^4 + 108*x^3 + 64*x^2 + 49*x + 112, x^41 + 76*x^39 + 60*x^38 + 54*x^37 + 20*x^36 + 60*x^35 + 4*x^34 + 37*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 118*x^5 + 52*x^4 + 28*x^3 + 100*x^2 + 121*x + 76, x^41 + 76*x^39 + 96*x^38 + 62*x^37 + 64*x^36 + 44*x^35 + 32*x^34 + 109*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 62*x^5 + 64*x^4 + 12*x^3 + 32*x^2 + x + 64, x^41 + 76*x^39 + 16*x^38 + 30*x^37 + 16*x^36 + 108*x^35 + 112*x^34 + 77*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 30*x^5 + 16*x^4 + 76*x^3 + 112*x^2 + 97*x + 112, x^41 + 76*x^39 + 104*x^38 + 94*x^37 + 120*x^36 + 44*x^35 + 88*x^34 + 77*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 94*x^5 + 56*x^4 + 12*x^3 + 24*x^2 + 97*x + 8, x^41 + 76*x^39 + 48*x^38 + 46*x^37 + 32*x^36 + 12*x^35 + 112*x^34 + 29*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 46*x^5 + 32*x^4 + 108*x^3 + 112*x^2 + 49*x + 64, x^41 + 76*x^39 + 28*x^38 + 86*x^37 + 52*x^36 + 60*x^35 + 100*x^34 + 5*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 22*x^5 + 84*x^4 + 28*x^3 + 68*x^2 + 89*x + 108, x^41 + 76*x^39 + 84*x^38 + 54*x^37 + 28*x^36 + 60*x^35 + 108*x^34 + 37*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 118*x^5 + 124*x^4 + 28*x^3 + 12*x^2 + 121*x + 4, x^41 + 76*x^39 + 28*x^38 + 54*x^37 + 84*x^36 + 124*x^35 + 36*x^34 + 101*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 118*x^5 + 116*x^4 + 92*x^3 + 4*x^2 + 57*x + 12, x^41 + 76*x^39 + 8*x^38 + 94*x^37 + 88*x^36 + 44*x^35 + 56*x^34 + 77*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 94*x^5 + 24*x^4 + 12*x^3 + 120*x^2 + 97*x + 40, x^41 + 76*x^39 + 24*x^38 + 94*x^37 + 8*x^36 + 108*x^35 + 104*x^34 + 13*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 94*x^5 + 72*x^4 + 76*x^3 + 40*x^2 + 33*x + 56, x^41 + 76*x^39 + 28*x^38 + 102*x^37 + 100*x^36 + 92*x^35 + 4*x^34 + 85*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 38*x^5 + 4*x^4 + 60*x^3 + 100*x^2 + 41*x + 28, x^41 + 76*x^39 + 28*x^38 + 22*x^37 + 52*x^36 + 124*x^35 + 36*x^34 + 5*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 86*x^5 + 84*x^4 + 92*x^3 + 4*x^2 + 89*x + 44, x^41 + 76*x^39 + 32*x^38 + 14*x^37 + 112*x^36 + 76*x^35 + 125*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 14*x^5 + 112*x^4 + 44*x^3 + 17*x + 112, x^41 + 76*x^39 + 56*x^38 + 78*x^37 + 120*x^36 + 76*x^35 + 40*x^34 + 61*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 78*x^5 + 56*x^4 + 44*x^3 + 104*x^2 + 81*x + 104, x^41 + 76*x^39 + 24*x^38 + 78*x^37 + 120*x^36 + 76*x^35 + 8*x^34 + 61*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 78*x^5 + 56*x^4 + 44*x^3 + 72*x^2 + 81*x + 40, x^41 + 76*x^39 + 48*x^38 + 94*x^37 + 16*x^36 + 44*x^35 + 80*x^34 + 77*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 94*x^5 + 16*x^4 + 12*x^3 + 80*x^2 + 97*x + 112, x^41 + 76*x^39 + 92*x^38 + 38*x^37 + 4*x^36 + 92*x^35 + 4*x^34 + 21*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 102*x^5 + 36*x^4 + 60*x^3 + 100*x^2 + 105*x + 60, x^41 + 76*x^39 + 4*x^38 + 54*x^37 + 108*x^36 + 60*x^35 + 60*x^34 + 37*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 118*x^5 + 76*x^4 + 28*x^3 + 92*x^2 + 121*x + 52, x^41 + 76*x^39 + 100*x^38 + 102*x^37 + 28*x^36 + 28*x^35 + 60*x^34 + 21*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 38*x^5 + 124*x^4 + 124*x^3 + 92*x^2 + 105*x + 36, x^41 + 76*x^39 + 72*x^38 + 94*x^37 + 88*x^36 + 44*x^35 + 120*x^34 + 77*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 94*x^5 + 24*x^4 + 12*x^3 + 56*x^2 + 97*x + 40, x^41 + 76*x^39 + 124*x^38 + 118*x^37 + 84*x^36 + 60*x^35 + 68*x^34 + 101*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 54*x^5 + 116*x^4 + 28*x^3 + 36*x^2 + 57*x + 12, x^41 + 76*x^39 + 88*x^38 + 62*x^37 + 72*x^36 + 108*x^35 + 104*x^34 + 45*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 62*x^5 + 8*x^4 + 76*x^3 + 40*x^2 + 65*x + 56, x^41 + 76*x^39 + 72*x^38 + 126*x^37 + 120*x^36 + 108*x^35 + 56*x^34 + 109*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 126*x^5 + 56*x^4 + 76*x^3 + 120*x^2 + x + 72, x^41 + 76*x^39 + 36*x^38 + 118*x^37 + 44*x^36 + 124*x^35 + 28*x^34 + 37*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 54*x^5 + 12*x^4 + 92*x^3 + 60*x^2 + 121*x + 116, x^41 + 76*x^39 + 108*x^38 + 6*x^37 + 116*x^36 + 92*x^35 + 52*x^34 + 53*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 70*x^5 + 20*x^4 + 60*x^3 + 20*x^2 + 9*x + 12, x^41 + 76*x^39 + 96*x^38 + 30*x^37 + 32*x^36 + 108*x^35 + 96*x^34 + 77*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 30*x^5 + 32*x^4 + 76*x^3 + 96*x^2 + 97*x + 32, x^41 + 76*x^39 + 80*x^38 + 62*x^37 + 48*x^36 + 44*x^35 + 112*x^34 + 109*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 62*x^5 + 48*x^4 + 12*x^3 + 112*x^2 + x + 16, x^41 + 76*x^39 + 108*x^38 + 38*x^37 + 116*x^36 + 92*x^35 + 116*x^34 + 21*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 102*x^5 + 20*x^4 + 60*x^3 + 84*x^2 + 105*x + 76, x^41 + 76*x^39 + 84*x^38 + 54*x^37 + 60*x^36 + 124*x^35 + 108*x^34 + 101*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 118*x^5 + 28*x^4 + 92*x^3 + 12*x^2 + 57*x + 100, x^41 + 76*x^39 + 72*x^38 + 46*x^37 + 8*x^36 + 76*x^35 + 24*x^34 + 93*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 46*x^5 + 72*x^4 + 44*x^3 + 88*x^2 + 113*x + 88, x^41 + 76*x^39 + 62*x^37 + 64*x^36 + 44*x^35 + 64*x^34 + 109*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 62*x^5 + 64*x^4 + 12*x^3 + 64*x^2 + x, x^41 + 76*x^39 + 100*x^38 + 38*x^37 + 124*x^36 + 92*x^35 + 60*x^34 + 21*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 102*x^5 + 92*x^4 + 60*x^3 + 92*x^2 + 105*x + 68, x^41 + 76*x^39 + 64*x^38 + 62*x^37 + 64*x^36 + 44*x^35 + 109*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 62*x^5 + 64*x^4 + 12*x^3 + x, x^41 + 76*x^39 + 64*x^38 + 46*x^37 + 16*x^36 + 12*x^35 + 96*x^34 + 29*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 46*x^5 + 16*x^4 + 108*x^3 + 96*x^2 + 49*x + 80, x^41 + 76*x^39 + 116*x^38 + 86*x^37 + 28*x^36 + 60*x^35 + 76*x^34 + 5*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 22*x^5 + 124*x^4 + 28*x^3 + 108*x^2 + 89*x + 4, x^41 + 76*x^39 + 32*x^38 + 110*x^37 + 80*x^36 + 12*x^35 + 64*x^34 + 93*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 110*x^5 + 80*x^4 + 108*x^3 + 64*x^2 + 113*x + 80, x^41 + 76*x^39 + 4*x^38 + 6*x^37 + 28*x^36 + 28*x^35 + 28*x^34 + 117*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 70*x^5 + 124*x^4 + 124*x^3 + 60*x^2 + 73*x + 36, x^41 + 76*x^39 + 28*x^38 + 6*x^37 + 68*x^36 + 92*x^35 + 4*x^34 + 53*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 70*x^5 + 100*x^4 + 60*x^3 + 100*x^2 + 9*x + 60, x^41 + 76*x^39 + 4*x^38 + 70*x^37 + 28*x^36 + 28*x^35 + 28*x^34 + 53*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 6*x^5 + 124*x^4 + 124*x^3 + 60*x^2 + 9*x + 36, x^41 + 76*x^39 + 4*x^38 + 118*x^37 + 108*x^36 + 124*x^35 + 124*x^34 + 37*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 54*x^5 + 76*x^4 + 92*x^3 + 28*x^2 + 121*x + 116, x^41 + 76*x^39 + 16*x^38 + 46*x^37 + 64*x^36 + 12*x^35 + 16*x^34 + 29*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 46*x^5 + 64*x^4 + 108*x^3 + 16*x^2 + 49*x + 32, x^41 + 76*x^39 + 84*x^38 + 6*x^37 + 44*x^36 + 28*x^35 + 12*x^34 + 117*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 70*x^5 + 12*x^4 + 124*x^3 + 44*x^2 + 73*x + 84, x^41 + 76*x^39 + 112*x^38 + 30*x^37 + 16*x^36 + 108*x^35 + 80*x^34 + 77*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 30*x^5 + 16*x^4 + 76*x^3 + 80*x^2 + 97*x + 48, x^41 + 76*x^39 + 92*x^38 + 38*x^37 + 4*x^36 + 28*x^35 + 68*x^34 + 85*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 102*x^5 + 36*x^4 + 124*x^3 + 36*x^2 + 41*x + 124, x^41 + 76*x^39 + 92*x^38 + 38*x^37 + 68*x^36 + 92*x^35 + 4*x^34 + 21*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 102*x^5 + 100*x^4 + 60*x^3 + 100*x^2 + 105*x + 124, x^41 + 76*x^39 + 56*x^38 + 62*x^37 + 8*x^36 + 108*x^35 + 72*x^34 + 45*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 62*x^5 + 72*x^4 + 76*x^3 + 8*x^2 + 65*x + 56, x^41 + 76*x^39 + 16*x^38 + 94*x^37 + 112*x^36 + 44*x^35 + 112*x^34 + 77*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 94*x^5 + 112*x^4 + 12*x^3 + 112*x^2 + 97*x + 16, x^41 + 76*x^39 + 104*x^38 + 46*x^37 + 40*x^36 + 76*x^35 + 120*x^34 + 93*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 46*x^5 + 104*x^4 + 44*x^3 + 56*x^2 + 113*x + 56, x^41 + 76*x^39 + 104*x^38 + 78*x^37 + 104*x^36 + 12*x^35 + 120*x^34 + 125*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 78*x^5 + 40*x^4 + 108*x^3 + 56*x^2 + 17*x + 120, x^41 + 76*x^39 + 116*x^38 + 102*x^37 + 76*x^36 + 92*x^35 + 108*x^34 + 85*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 38*x^5 + 44*x^4 + 60*x^3 + 12*x^2 + 41*x + 52, x^41 + 76*x^39 + 104*x^38 + 78*x^37 + 8*x^36 + 76*x^35 + 120*x^34 + 61*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 78*x^5 + 72*x^4 + 44*x^3 + 56*x^2 + 81*x + 88, x^41 + 76*x^39 + 32*x^38 + 30*x^37 + 64*x^36 + 108*x^35 + 96*x^34 + 77*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 30*x^5 + 64*x^4 + 76*x^3 + 96*x^2 + 97*x + 64, x^41 + 76*x^39 + 78*x^37 + 16*x^36 + 12*x^35 + 96*x^34 + 125*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 78*x^5 + 16*x^4 + 108*x^3 + 96*x^2 + 17*x + 16, x^41 + 76*x^39 + 28*x^38 + 86*x^37 + 20*x^36 + 124*x^35 + 100*x^34 + 69*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 22*x^5 + 52*x^4 + 92*x^3 + 68*x^2 + 25*x + 12, x^41 + 76*x^39 + 72*x^38 + 46*x^37 + 104*x^36 + 12*x^35 + 24*x^34 + 29*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 46*x^5 + 40*x^4 + 108*x^3 + 88*x^2 + 49*x + 120, x^41 + 76*x^39 + 80*x^38 + 78*x^37 + 76*x^35 + 80*x^34 + 61*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 78*x^5 + 44*x^3 + 80*x^2 + 81*x + 96, x^41 + 76*x^39 + 36*x^38 + 54*x^37 + 44*x^36 + 60*x^35 + 92*x^34 + 37*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 118*x^5 + 12*x^4 + 28*x^3 + 124*x^2 + 121*x + 52, x^41 + 76*x^39 + 28*x^38 + 118*x^37 + 116*x^36 + 124*x^35 + 100*x^34 + 37*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 54*x^5 + 20*x^4 + 92*x^3 + 68*x^2 + 121*x + 44, x^41 + 76*x^39 + 12*x^38 + 118*x^37 + 68*x^36 + 60*x^35 + 52*x^34 + 101*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 54*x^5 + 100*x^4 + 28*x^3 + 20*x^2 + 57*x + 28, x^41 + 76*x^39 + 100*x^38 + 38*x^37 + 60*x^36 + 28*x^35 + 124*x^34 + 85*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 102*x^5 + 28*x^4 + 124*x^3 + 28*x^2 + 41*x + 68, x^41 + 76*x^39 + 104*x^38 + 110*x^37 + 40*x^36 + 12*x^35 + 56*x^34 + 93*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 110*x^5 + 104*x^4 + 108*x^3 + 120*x^2 + 113*x + 120, x^41 + 76*x^39 + 64*x^38 + 46*x^37 + 80*x^36 + 12*x^35 + 96*x^34 + 29*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 46*x^5 + 80*x^4 + 108*x^3 + 96*x^2 + 49*x + 16, x^41 + 76*x^39 + 120*x^38 + 126*x^37 + 8*x^36 + 44*x^35 + 72*x^34 + 45*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 126*x^5 + 72*x^4 + 12*x^3 + 8*x^2 + 65*x + 120, x^41 + 76*x^39 + 40*x^38 + 62*x^37 + 88*x^36 + 108*x^35 + 88*x^34 + 45*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 62*x^5 + 24*x^4 + 76*x^3 + 24*x^2 + 65*x + 104, x^41 + 76*x^39 + 28*x^38 + 22*x^37 + 116*x^36 + 124*x^35 + 36*x^34 + 5*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 86*x^5 + 20*x^4 + 92*x^3 + 4*x^2 + 89*x + 108, x^41 + 76*x^39 + 72*x^38 + 94*x^37 + 88*x^36 + 108*x^35 + 56*x^34 + 13*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 94*x^5 + 24*x^4 + 76*x^3 + 120*x^2 + 33*x + 104, x^41 + 76*x^39 + 52*x^38 + 70*x^37 + 44*x^36 + 92*x^35 + 44*x^34 + 117*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 6*x^5 + 12*x^4 + 60*x^3 + 76*x^2 + 73*x + 84, x^41 + 76*x^39 + 52*x^38 + 6*x^37 + 44*x^36 + 92*x^35 + 44*x^34 + 53*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 70*x^5 + 12*x^4 + 60*x^3 + 76*x^2 + 9*x + 84, x^41 + 76*x^39 + 20*x^38 + 54*x^37 + 28*x^36 + 124*x^35 + 108*x^34 + 101*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 118*x^5 + 124*x^4 + 92*x^3 + 12*x^2 + 57*x + 68, x^41 + 76*x^39 + 84*x^38 + 70*x^37 + 44*x^36 + 28*x^35 + 12*x^34 + 53*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 6*x^5 + 12*x^4 + 124*x^3 + 44*x^2 + 9*x + 84, x^41 + 76*x^39 + 68*x^38 + 22*x^37 + 12*x^36 + 60*x^35 + 124*x^34 + 69*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 86*x^5 + 108*x^4 + 28*x^3 + 28*x^2 + 25*x + 20, x^41 + 76*x^39 + 16*x^38 + 94*x^37 + 80*x^36 + 108*x^35 + 112*x^34 + 13*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 94*x^5 + 80*x^4 + 76*x^3 + 112*x^2 + 33*x + 48, x^41 + 76*x^39 + 68*x^38 + 6*x^37 + 124*x^36 + 28*x^35 + 28*x^34 + 117*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 70*x^5 + 92*x^4 + 124*x^3 + 60*x^2 + 73*x + 4, x^41 + 76*x^39 + 76*x^38 + 38*x^37 + 52*x^36 + 92*x^35 + 84*x^34 + 21*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 102*x^5 + 84*x^4 + 60*x^3 + 52*x^2 + 105*x + 76, x^41 + 76*x^39 + 48*x^38 + 126*x^37 + 48*x^36 + 44*x^35 + 80*x^34 + 45*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 126*x^5 + 48*x^4 + 12*x^3 + 80*x^2 + 65*x + 80, x^41 + 76*x^39 + 96*x^38 + 30*x^37 + 64*x^36 + 108*x^35 + 32*x^34 + 77*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 30*x^5 + 64*x^4 + 76*x^3 + 32*x^2 + 97*x + 64, x^41 + 76*x^39 + 8*x^38 + 78*x^37 + 104*x^36 + 12*x^35 + 24*x^34 + 125*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 78*x^5 + 40*x^4 + 108*x^3 + 88*x^2 + 17*x + 56, x^41 + 76*x^39 + 56*x^38 + 14*x^37 + 56*x^36 + 12*x^35 + 104*x^34 + 61*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 14*x^5 + 120*x^4 + 108*x^3 + 40*x^2 + 81*x + 104, x^41 + 76*x^39 + 4*x^38 + 70*x^37 + 28*x^36 + 92*x^35 + 92*x^34 + 117*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 6*x^5 + 124*x^4 + 60*x^3 + 124*x^2 + 73*x + 100, x^41 + 76*x^39 + 14*x^37 + 80*x^36 + 76*x^35 + 32*x^34 + 125*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 14*x^5 + 80*x^4 + 44*x^3 + 32*x^2 + 17*x + 16, x^41 + 76*x^39 + 120*x^38 + 46*x^37 + 120*x^36 + 12*x^35 + 104*x^34 + 29*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 46*x^5 + 56*x^4 + 108*x^3 + 40*x^2 + 49*x + 104, x^41 + 76*x^39 + 4*x^38 + 6*x^37 + 28*x^36 + 92*x^35 + 92*x^34 + 53*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 70*x^5 + 124*x^4 + 60*x^3 + 124*x^2 + 9*x + 100, x^41 + 76*x^39 + 28*x^38 + 118*x^37 + 84*x^36 + 60*x^35 + 100*x^34 + 101*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 54*x^5 + 116*x^4 + 28*x^3 + 68*x^2 + 57*x + 76, x^41 + 76*x^39 + 100*x^38 + 86*x^37 + 44*x^36 + 60*x^35 + 92*x^34 + 5*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 22*x^5 + 12*x^4 + 28*x^3 + 124*x^2 + 89*x + 116, x^41 + 76*x^39 + 84*x^38 + 6*x^37 + 44*x^36 + 92*x^35 + 76*x^34 + 53*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 70*x^5 + 12*x^4 + 60*x^3 + 108*x^2 + 9*x + 20, x^41 + 76*x^39 + 108*x^38 + 38*x^37 + 52*x^36 + 28*x^35 + 52*x^34 + 85*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 102*x^5 + 84*x^4 + 124*x^3 + 20*x^2 + 41*x + 76, x^41 + 76*x^39 + 12*x^38 + 118*x^37 + 4*x^36 + 60*x^35 + 52*x^34 + 101*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 54*x^5 + 36*x^4 + 28*x^3 + 20*x^2 + 57*x + 92, x^41 + 76*x^39 + 8*x^38 + 46*x^37 + 72*x^36 + 76*x^35 + 88*x^34 + 93*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 46*x^5 + 8*x^4 + 44*x^3 + 24*x^2 + 113*x + 24, x^41 + 76*x^39 + 52*x^38 + 54*x^37 + 28*x^36 + 124*x^35 + 12*x^34 + 101*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 118*x^5 + 124*x^4 + 92*x^3 + 44*x^2 + 57*x + 4, x^41 + 76*x^39 + 4*x^38 + 102*x^37 + 92*x^36 + 28*x^35 + 92*x^34 + 21*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 38*x^5 + 60*x^4 + 124*x^3 + 124*x^2 + 105*x + 36, x^41 + 76*x^39 + 4*x^38 + 86*x^37 + 76*x^36 + 60*x^35 + 60*x^34 + 5*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 22*x^5 + 44*x^4 + 28*x^3 + 92*x^2 + 89*x + 84, x^41 + 76*x^39 + 8*x^38 + 94*x^37 + 120*x^36 + 108*x^35 + 56*x^34 + 13*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 94*x^5 + 56*x^4 + 76*x^3 + 120*x^2 + 33*x + 8, x^41 + 76*x^39 + 56*x^38 + 62*x^37 + 104*x^36 + 108*x^35 + 8*x^34 + 45*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 62*x^5 + 40*x^4 + 76*x^3 + 72*x^2 + 65*x + 24, x^41 + 76*x^39 + 104*x^38 + 110*x^37 + 104*x^36 + 76*x^35 + 120*x^34 + 29*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 110*x^5 + 40*x^4 + 44*x^3 + 56*x^2 + 49*x + 120, x^41 + 76*x^39 + 46*x^37 + 48*x^36 + 12*x^35 + 96*x^34 + 29*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 46*x^5 + 48*x^4 + 108*x^3 + 96*x^2 + 49*x + 112, x^41 + 76*x^39 + 32*x^38 + 110*x^37 + 112*x^36 + 12*x^35 + 93*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 110*x^5 + 112*x^4 + 108*x^3 + 113*x + 112, x^41 + 76*x^39 + 104*x^38 + 62*x^37 + 88*x^36 + 108*x^35 + 24*x^34 + 45*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 62*x^5 + 24*x^4 + 76*x^3 + 88*x^2 + 65*x + 104, x^41 + 76*x^39 + 72*x^38 + 110*x^37 + 72*x^36 + 76*x^35 + 24*x^34 + 29*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 110*x^5 + 8*x^4 + 44*x^3 + 88*x^2 + 49*x + 24, x^41 + 76*x^39 + 92*x^38 + 6*x^37 + 4*x^36 + 28*x^35 + 4*x^34 + 117*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 70*x^5 + 36*x^4 + 124*x^3 + 100*x^2 + 73*x + 60, x^41 + 76*x^39 + 100*x^38 + 38*x^37 + 92*x^36 + 28*x^35 + 60*x^34 + 85*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 102*x^5 + 60*x^4 + 124*x^3 + 92*x^2 + 41*x + 100, x^41 + 76*x^39 + 12*x^38 + 6*x^37 + 20*x^36 + 92*x^35 + 20*x^34 + 53*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 70*x^5 + 52*x^4 + 60*x^3 + 116*x^2 + 9*x + 108, x^41 + 76*x^39 + 40*x^38 + 126*x^37 + 120*x^36 + 44*x^35 + 88*x^34 + 45*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 126*x^5 + 56*x^4 + 12*x^3 + 24*x^2 + 65*x + 72, x^41 + 76*x^39 + 56*x^38 + 46*x^37 + 24*x^36 + 76*x^35 + 40*x^34 + 93*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 46*x^5 + 88*x^4 + 44*x^3 + 104*x^2 + 113*x + 72, x^41 + 76*x^39 + 68*x^38 + 86*x^37 + 108*x^36 + 124*x^35 + 124*x^34 + 69*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 22*x^5 + 76*x^4 + 92*x^3 + 28*x^2 + 25*x + 52, x^41 + 76*x^39 + 104*x^38 + 126*x^37 + 24*x^36 + 44*x^35 + 88*x^34 + 45*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 126*x^5 + 88*x^4 + 12*x^3 + 24*x^2 + 65*x + 104, x^41 + 76*x^39 + 96*x^38 + 14*x^37 + 48*x^36 + 76*x^35 + 64*x^34 + 125*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 14*x^5 + 48*x^4 + 44*x^3 + 64*x^2 + 17*x + 48, x^41 + 76*x^39 + 46*x^37 + 80*x^36 + 76*x^35 + 96*x^34 + 93*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 46*x^5 + 80*x^4 + 44*x^3 + 96*x^2 + 113*x + 80, x^41 + 76*x^39 + 92*x^38 + 54*x^37 + 20*x^36 + 60*x^35 + 36*x^34 + 37*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 118*x^5 + 52*x^4 + 28*x^3 + 4*x^2 + 121*x + 12, x^41 + 76*x^39 + 16*x^38 + 46*x^37 + 76*x^35 + 80*x^34 + 93*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 46*x^5 + 44*x^3 + 80*x^2 + 113*x + 32, x^41 + 76*x^39 + 56*x^38 + 78*x^37 + 88*x^36 + 76*x^35 + 104*x^34 + 61*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 78*x^5 + 24*x^4 + 44*x^3 + 40*x^2 + 81*x + 72, x^41 + 76*x^39 + 12*x^38 + 22*x^37 + 4*x^36 + 60*x^35 + 116*x^34 + 69*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 86*x^5 + 36*x^4 + 28*x^3 + 84*x^2 + 25*x + 28, x^41 + 76*x^39 + 100*x^38 + 102*x^37 + 124*x^36 + 28*x^35 + 124*x^34 + 21*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 38*x^5 + 92*x^4 + 124*x^3 + 28*x^2 + 105*x + 4, x^41 + 76*x^39 + 126*x^37 + 64*x^36 + 44*x^35 + 64*x^34 + 45*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 126*x^5 + 64*x^4 + 12*x^3 + 64*x^2 + 65*x, x^41 + 76*x^39 + 16*x^38 + 94*x^37 + 16*x^36 + 44*x^35 + 48*x^34 + 77*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 94*x^5 + 16*x^4 + 12*x^3 + 48*x^2 + 97*x + 48, x^41 + 76*x^39 + 36*x^38 + 38*x^37 + 60*x^36 + 92*x^35 + 124*x^34 + 21*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 102*x^5 + 28*x^4 + 60*x^3 + 28*x^2 + 105*x + 4, x^41 + 76*x^39 + 64*x^38 + 126*x^37 + 64*x^36 + 44*x^35 + 45*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 126*x^5 + 64*x^4 + 12*x^3 + 65*x, x^41 + 76*x^39 + 100*x^38 + 70*x^37 + 28*x^36 + 28*x^35 + 124*x^34 + 53*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 6*x^5 + 124*x^4 + 124*x^3 + 28*x^2 + 9*x + 100, x^41 + 76*x^39 + 46*x^37 + 112*x^36 + 12*x^35 + 96*x^34 + 29*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 46*x^5 + 112*x^4 + 108*x^3 + 96*x^2 + 49*x + 48, x^41 + 76*x^39 + 56*x^38 + 110*x^37 + 24*x^36 + 12*x^35 + 104*x^34 + 93*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 110*x^5 + 88*x^4 + 108*x^3 + 40*x^2 + 113*x + 8, x^41 + 76*x^39 + 120*x^38 + 78*x^37 + 88*x^36 + 12*x^35 + 104*x^34 + 125*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 78*x^5 + 24*x^4 + 108*x^3 + 40*x^2 + 17*x + 8, x^41 + 76*x^39 + 100*x^38 + 70*x^37 + 60*x^36 + 28*x^35 + 60*x^34 + 53*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 6*x^5 + 28*x^4 + 124*x^3 + 92*x^2 + 9*x + 4, x^41 + 76*x^39 + 40*x^38 + 30*x^37 + 88*x^36 + 44*x^35 + 88*x^34 + 13*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 30*x^5 + 24*x^4 + 12*x^3 + 24*x^2 + 33*x + 104, x^41 + 76*x^39 + 32*x^38 + 30*x^37 + 32*x^36 + 108*x^35 + 32*x^34 + 77*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 30*x^5 + 32*x^4 + 76*x^3 + 32*x^2 + 97*x + 32, x^41 + 76*x^39 + 88*x^38 + 14*x^37 + 24*x^36 + 76*x^35 + 8*x^34 + 125*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 14*x^5 + 88*x^4 + 44*x^3 + 72*x^2 + 17*x + 72, x^41 + 76*x^39 + 44*x^38 + 54*x^37 + 36*x^36 + 124*x^35 + 84*x^34 + 101*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 118*x^5 + 68*x^4 + 92*x^3 + 52*x^2 + 57*x + 124, x^41 + 76*x^39 + 64*x^38 + 46*x^37 + 48*x^36 + 12*x^35 + 32*x^34 + 29*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 46*x^5 + 48*x^4 + 108*x^3 + 32*x^2 + 49*x + 112, x^41 + 76*x^39 + 28*x^38 + 38*x^37 + 100*x^36 + 92*x^35 + 4*x^34 + 21*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 102*x^5 + 4*x^4 + 60*x^3 + 100*x^2 + 105*x + 28, x^41 + 76*x^39 + 52*x^38 + 6*x^37 + 44*x^36 + 28*x^35 + 108*x^34 + 117*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 70*x^5 + 12*x^4 + 124*x^3 + 12*x^2 + 73*x + 20, x^41 + 76*x^39 + 52*x^38 + 70*x^37 + 44*x^36 + 28*x^35 + 108*x^34 + 53*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 6*x^5 + 12*x^4 + 124*x^3 + 12*x^2 + 9*x + 20, x^41 + 76*x^39 + 68*x^38 + 6*x^37 + 28*x^36 + 92*x^35 + 28*x^34 + 53*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 70*x^5 + 124*x^4 + 60*x^3 + 60*x^2 + 9*x + 100, x^41 + 76*x^39 + 84*x^38 + 70*x^37 + 44*x^36 + 92*x^35 + 76*x^34 + 117*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 6*x^5 + 12*x^4 + 60*x^3 + 108*x^2 + 73*x + 20, x^41 + 76*x^39 + 104*x^38 + 46*x^37 + 104*x^36 + 76*x^35 + 120*x^34 + 93*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 46*x^5 + 40*x^4 + 44*x^3 + 56*x^2 + 113*x + 120, x^41 + 76*x^39 + 110*x^37 + 16*x^36 + 12*x^35 + 32*x^34 + 93*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 110*x^5 + 16*x^4 + 108*x^3 + 32*x^2 + 113*x + 80, x^41 + 76*x^39 + 12*x^38 + 38*x^37 + 116*x^36 + 92*x^35 + 20*x^34 + 21*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 102*x^5 + 20*x^4 + 60*x^3 + 116*x^2 + 105*x + 12, x^41 + 76*x^39 + 40*x^38 + 78*x^37 + 8*x^36 + 12*x^35 + 120*x^34 + 125*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 78*x^5 + 72*x^4 + 108*x^3 + 56*x^2 + 17*x + 24, x^41 + 76*x^39 + 100*x^38 + 6*x^37 + 28*x^36 + 28*x^35 + 124*x^34 + 117*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 70*x^5 + 124*x^4 + 124*x^3 + 28*x^2 + 73*x + 100, x^41 + 76*x^39 + 48*x^38 + 110*x^37 + 76*x^35 + 112*x^34 + 29*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 110*x^5 + 44*x^3 + 112*x^2 + 49*x + 96, x^41 + 76*x^39 + 8*x^38 + 62*x^37 + 120*x^36 + 108*x^35 + 120*x^34 + 45*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 62*x^5 + 56*x^4 + 76*x^3 + 56*x^2 + 65*x + 72, x^41 + 76*x^39 + 112*x^38 + 110*x^37 + 96*x^36 + 76*x^35 + 112*x^34 + 29*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 110*x^5 + 96*x^4 + 44*x^3 + 112*x^2 + 49*x + 64, x^41 + 76*x^39 + 92*x^38 + 22*x^37 + 20*x^36 + 60*x^35 + 100*x^34 + 69*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 86*x^5 + 52*x^4 + 28*x^3 + 68*x^2 + 25*x + 76, x^41 + 76*x^39 + 108*x^38 + 6*x^37 + 52*x^36 + 28*x^35 + 116*x^34 + 117*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 70*x^5 + 84*x^4 + 124*x^3 + 84*x^2 + 73*x + 12, x^41 + 76*x^39 + 92*x^38 + 102*x^37 + 100*x^36 + 28*x^35 + 4*x^34 + 21*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 38*x^5 + 4*x^4 + 124*x^3 + 100*x^2 + 105*x + 92, x^41 + 76*x^39 + 104*x^38 + 62*x^37 + 120*x^36 + 44*x^35 + 24*x^34 + 109*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 62*x^5 + 56*x^4 + 12*x^3 + 88*x^2 + x + 72, x^41 + 76*x^39 + 100*x^38 + 70*x^37 + 60*x^36 + 92*x^35 + 124*x^34 + 117*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 6*x^5 + 28*x^4 + 60*x^3 + 28*x^2 + 73*x + 68, x^41 + 76*x^39 + 20*x^38 + 22*x^37 + 60*x^36 + 124*x^35 + 108*x^34 + 5*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 86*x^5 + 28*x^4 + 92*x^3 + 12*x^2 + 89*x + 36, x^41 + 76*x^39 + 36*x^38 + 70*x^37 + 124*x^36 + 28*x^35 + 124*x^34 + 53*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 6*x^5 + 92*x^4 + 124*x^3 + 28*x^2 + 9*x + 68, x^41 + 76*x^39 + 104*x^38 + 94*x^37 + 24*x^36 + 108*x^35 + 88*x^34 + 13*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 94*x^5 + 88*x^4 + 76*x^3 + 24*x^2 + 33*x + 104, x^41 + 76*x^39 + 80*x^38 + 46*x^37 + 64*x^36 + 76*x^35 + 16*x^34 + 93*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 46*x^5 + 64*x^4 + 44*x^3 + 16*x^2 + 113*x + 96, x^41 + 76*x^39 + 36*x^38 + 118*x^37 + 12*x^36 + 60*x^35 + 28*x^34 + 101*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 54*x^5 + 108*x^4 + 28*x^3 + 60*x^2 + 57*x + 20, x^41 + 76*x^39 + 36*x^38 + 102*x^37 + 92*x^36 + 28*x^35 + 124*x^34 + 21*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 38*x^5 + 60*x^4 + 124*x^3 + 28*x^2 + 105*x + 100, x^41 + 76*x^39 + 76*x^38 + 118*x^37 + 100*x^36 + 60*x^35 + 52*x^34 + 101*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 54*x^5 + 4*x^4 + 28*x^3 + 20*x^2 + 57*x + 60, x^41 + 76*x^39 + 76*x^38 + 22*x^37 + 36*x^36 + 124*x^35 + 52*x^34 + 5*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 86*x^5 + 68*x^4 + 92*x^3 + 20*x^2 + 89*x + 124, x^41 + 76*x^39 + 20*x^38 + 118*x^37 + 124*x^36 + 60*x^35 + 108*x^34 + 101*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 54*x^5 + 92*x^4 + 28*x^3 + 12*x^2 + 57*x + 100, x^41 + 76*x^39 + 8*x^38 + 46*x^37 + 104*x^36 + 76*x^35 + 24*x^34 + 93*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 46*x^5 + 40*x^4 + 44*x^3 + 88*x^2 + 113*x + 56, x^41 + 76*x^39 + 8*x^38 + 110*x^37 + 104*x^36 + 76*x^35 + 24*x^34 + 29*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 110*x^5 + 40*x^4 + 44*x^3 + 88*x^2 + 49*x + 56, x^41 + 76*x^39 + 8*x^38 + 30*x^37 + 56*x^36 + 108*x^35 + 56*x^34 + 77*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 30*x^5 + 120*x^4 + 76*x^3 + 120*x^2 + 97*x + 72, x^41 + 76*x^39 + 8*x^38 + 46*x^37 + 104*x^36 + 12*x^35 + 88*x^34 + 29*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 46*x^5 + 40*x^4 + 108*x^3 + 24*x^2 + 49*x + 120, x^41 + 76*x^39 + 112*x^38 + 78*x^37 + 12*x^35 + 48*x^34 + 125*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 78*x^5 + 108*x^3 + 48*x^2 + 17*x + 96, x^41 + 76*x^39 + 52*x^38 + 6*x^37 + 12*x^36 + 28*x^35 + 44*x^34 + 117*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 70*x^5 + 108*x^4 + 124*x^3 + 76*x^2 + 73*x + 116, x^41 + 76*x^39 + 120*x^38 + 78*x^37 + 120*x^36 + 12*x^35 + 40*x^34 + 125*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 78*x^5 + 56*x^4 + 108*x^3 + 104*x^2 + 17*x + 40, x^41 + 76*x^39 + 110*x^37 + 80*x^36 + 12*x^35 + 32*x^34 + 93*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 110*x^5 + 80*x^4 + 108*x^3 + 32*x^2 + 113*x + 16, x^41 + 76*x^39 + 100*x^38 + 70*x^37 + 92*x^36 + 28*x^35 + 124*x^34 + 53*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 6*x^5 + 60*x^4 + 124*x^3 + 28*x^2 + 9*x + 36, x^41 + 76*x^39 + 8*x^38 + 14*x^37 + 72*x^36 + 76*x^35 + 24*x^34 + 125*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 14*x^5 + 8*x^4 + 44*x^3 + 88*x^2 + 17*x + 88, x^41 + 76*x^39 + 96*x^38 + 62*x^37 + 32*x^36 + 108*x^35 + 32*x^34 + 45*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 62*x^5 + 32*x^4 + 76*x^3 + 32*x^2 + 65*x + 96, x^41 + 76*x^39 + 96*x^38 + 46*x^37 + 16*x^36 + 12*x^35 + 29*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 46*x^5 + 16*x^4 + 108*x^3 + 49*x + 16, x^41 + 76*x^39 + 20*x^38 + 86*x^37 + 60*x^36 + 124*x^35 + 108*x^34 + 69*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 22*x^5 + 28*x^4 + 92*x^3 + 12*x^2 + 25*x + 36, x^41 + 76*x^39 + 40*x^38 + 62*x^37 + 56*x^36 + 108*x^35 + 24*x^34 + 45*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 62*x^5 + 120*x^4 + 76*x^3 + 88*x^2 + 65*x + 72, x^41 + 76*x^39 + 84*x^38 + 86*x^37 + 60*x^36 + 60*x^35 + 108*x^34 + 5*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 22*x^5 + 28*x^4 + 28*x^3 + 12*x^2 + 89*x + 100, x^41 + 76*x^39 + 124*x^38 + 22*x^37 + 52*x^36 + 60*x^35 + 68*x^34 + 69*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 86*x^5 + 84*x^4 + 28*x^3 + 36*x^2 + 25*x + 44, x^41 + 76*x^39 + 12*x^38 + 86*x^37 + 68*x^36 + 60*x^35 + 116*x^34 + 5*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 22*x^5 + 100*x^4 + 28*x^3 + 84*x^2 + 89*x + 92, x^41 + 76*x^39 + 64*x^38 + 30*x^37 + 96*x^36 + 108*x^35 + 64*x^34 + 77*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 30*x^5 + 96*x^4 + 76*x^3 + 64*x^2 + 97*x + 32, x^41 + 76*x^39 + 4*x^38 + 6*x^37 + 60*x^36 + 92*x^35 + 28*x^34 + 53*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 70*x^5 + 28*x^4 + 60*x^3 + 60*x^2 + 9*x + 4, x^41 + 76*x^39 + 72*x^38 + 110*x^37 + 104*x^36 + 12*x^35 + 24*x^34 + 93*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 110*x^5 + 40*x^4 + 108*x^3 + 88*x^2 + 113*x + 120, x^41 + 76*x^39 + 88*x^38 + 94*x^37 + 40*x^36 + 44*x^35 + 40*x^34 + 77*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 94*x^5 + 104*x^4 + 12*x^3 + 104*x^2 + 97*x + 24, x^41 + 76*x^39 + 30*x^37 + 96*x^36 + 44*x^35 + 64*x^34 + 13*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 30*x^5 + 96*x^4 + 12*x^3 + 64*x^2 + 33*x + 96, x^41 + 76*x^39 + 124*x^38 + 54*x^37 + 116*x^36 + 124*x^35 + 68*x^34 + 101*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 118*x^5 + 20*x^4 + 92*x^3 + 36*x^2 + 57*x + 108, x^41 + 76*x^39 + 104*x^38 + 78*x^37 + 72*x^36 + 76*x^35 + 120*x^34 + 61*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 78*x^5 + 8*x^4 + 44*x^3 + 56*x^2 + 81*x + 24, x^41 + 76*x^39 + 28*x^38 + 54*x^37 + 20*x^36 + 124*x^35 + 36*x^34 + 101*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 118*x^5 + 52*x^4 + 92*x^3 + 4*x^2 + 57*x + 76, x^41 + 76*x^39 + 40*x^38 + 126*x^37 + 88*x^36 + 108*x^35 + 88*x^34 + 109*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 126*x^5 + 24*x^4 + 76*x^3 + 24*x^2 + x + 104, x^41 + 76*x^39 + 76*x^38 + 22*x^37 + 4*x^36 + 60*x^35 + 52*x^34 + 69*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 86*x^5 + 36*x^4 + 28*x^3 + 20*x^2 + 25*x + 28, x^41 + 76*x^39 + 108*x^38 + 86*x^37 + 4*x^36 + 60*x^35 + 84*x^34 + 5*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 22*x^5 + 36*x^4 + 28*x^3 + 52*x^2 + 89*x + 92, x^41 + 76*x^39 + 56*x^38 + 126*x^37 + 104*x^36 + 108*x^35 + 8*x^34 + 109*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 126*x^5 + 40*x^4 + 76*x^3 + 72*x^2 + x + 24, x^41 + 76*x^39 + 84*x^38 + 102*x^37 + 12*x^36 + 92*x^35 + 76*x^34 + 85*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 38*x^5 + 108*x^4 + 60*x^3 + 108*x^2 + 41*x + 52, x^41 + 76*x^39 + 76*x^38 + 38*x^37 + 52*x^36 + 28*x^35 + 20*x^34 + 85*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 102*x^5 + 84*x^4 + 124*x^3 + 116*x^2 + 41*x + 12, x^41 + 76*x^39 + 64*x^38 + 30*x^37 + 96*x^36 + 44*x^35 + 13*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 30*x^5 + 96*x^4 + 12*x^3 + 33*x + 96, x^41 + 76*x^39 + 40*x^38 + 46*x^37 + 104*x^36 + 12*x^35 + 120*x^34 + 29*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 46*x^5 + 40*x^4 + 108*x^3 + 56*x^2 + 49*x + 56, x^41 + 76*x^39 + 96*x^38 + 62*x^37 + 96*x^36 + 108*x^35 + 32*x^34 + 45*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 62*x^5 + 96*x^4 + 76*x^3 + 32*x^2 + 65*x + 32, x^41 + 76*x^39 + 72*x^38 + 30*x^37 + 24*x^36 + 44*x^35 + 120*x^34 + 13*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 30*x^5 + 88*x^4 + 12*x^3 + 56*x^2 + 33*x + 104, x^41 + 76*x^39 + 96*x^38 + 110*x^37 + 48*x^36 + 12*x^35 + 64*x^34 + 93*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 110*x^5 + 48*x^4 + 108*x^3 + 64*x^2 + 113*x + 48, x^41 + 76*x^39 + 78*x^37 + 80*x^36 + 12*x^35 + 96*x^34 + 125*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 78*x^5 + 80*x^4 + 108*x^3 + 96*x^2 + 17*x + 80, x^41 + 76*x^39 + 88*x^38 + 46*x^37 + 56*x^36 + 12*x^35 + 72*x^34 + 29*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 46*x^5 + 120*x^4 + 108*x^3 + 8*x^2 + 49*x + 104, x^41 + 76*x^39 + 108*x^38 + 38*x^37 + 52*x^36 + 92*x^35 + 116*x^34 + 21*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 102*x^5 + 84*x^4 + 60*x^3 + 84*x^2 + 105*x + 12, x^41 + 76*x^39 + 46*x^37 + 16*x^36 + 12*x^35 + 32*x^34 + 29*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 46*x^5 + 16*x^4 + 108*x^3 + 32*x^2 + 49*x + 80, x^41 + 76*x^39 + 100*x^38 + 86*x^37 + 76*x^36 + 124*x^35 + 92*x^34 + 69*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 22*x^5 + 44*x^4 + 92*x^3 + 124*x^2 + 25*x + 84, x^41 + 76*x^39 + 16*x^38 + 78*x^37 + 12*x^35 + 80*x^34 + 125*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 78*x^5 + 108*x^3 + 80*x^2 + 17*x + 32, x^41 + 76*x^39 + 40*x^38 + 30*x^37 + 56*x^36 + 44*x^35 + 24*x^34 + 13*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 30*x^5 + 120*x^4 + 12*x^3 + 88*x^2 + 33*x + 72, x^41 + 76*x^39 + 28*x^38 + 102*x^37 + 36*x^36 + 92*x^35 + 4*x^34 + 85*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 38*x^5 + 68*x^4 + 60*x^3 + 100*x^2 + 41*x + 92, x^41 + 76*x^39 + 28*x^38 + 54*x^37 + 84*x^36 + 60*x^35 + 100*x^34 + 37*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 118*x^5 + 116*x^4 + 28*x^3 + 68*x^2 + 121*x + 76, x^41 + 76*x^39 + 32*x^38 + 46*x^37 + 16*x^36 + 76*x^35 + 93*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 46*x^5 + 16*x^4 + 44*x^3 + 113*x + 80, x^41 + 76*x^39 + 20*x^38 + 54*x^37 + 60*x^36 + 124*x^35 + 44*x^34 + 101*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 118*x^5 + 28*x^4 + 92*x^3 + 76*x^2 + 57*x + 100, x^41 + 76*x^39 + 72*x^38 + 94*x^37 + 56*x^36 + 44*x^35 + 56*x^34 + 77*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 94*x^5 + 120*x^4 + 12*x^3 + 120*x^2 + 97*x + 8, x^41 + 76*x^39 + 124*x^38 + 6*x^37 + 68*x^36 + 92*x^35 + 100*x^34 + 53*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 70*x^5 + 100*x^4 + 60*x^3 + 68*x^2 + 9*x + 124, x^41 + 76*x^39 + 56*x^38 + 110*x^37 + 120*x^36 + 12*x^35 + 40*x^34 + 93*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 110*x^5 + 56*x^4 + 108*x^3 + 104*x^2 + 113*x + 104, x^41 + 76*x^39 + 52*x^38 + 118*x^37 + 28*x^36 + 124*x^35 + 12*x^34 + 37*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 54*x^5 + 124*x^4 + 92*x^3 + 44*x^2 + 121*x + 4, x^41 + 76*x^39 + 120*x^38 + 30*x^37 + 104*x^36 + 108*x^35 + 8*x^34 + 77*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 30*x^5 + 40*x^4 + 76*x^3 + 72*x^2 + 97*x + 88, x^41 + 76*x^39 + 36*x^38 + 6*x^37 + 92*x^36 + 28*x^35 + 60*x^34 + 117*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 70*x^5 + 60*x^4 + 124*x^3 + 92*x^2 + 73*x + 36, x^41 + 76*x^39 + 112*x^38 + 110*x^37 + 32*x^36 + 76*x^35 + 112*x^34 + 29*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 110*x^5 + 32*x^4 + 44*x^3 + 112*x^2 + 49*x, x^41 + 76*x^39 + 12*x^38 + 70*x^37 + 20*x^36 + 28*x^35 + 84*x^34 + 53*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 6*x^5 + 52*x^4 + 124*x^3 + 52*x^2 + 9*x + 44, x^41 + 76*x^39 + 20*x^38 + 22*x^37 + 124*x^36 + 60*x^35 + 44*x^34 + 69*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 86*x^5 + 92*x^4 + 28*x^3 + 76*x^2 + 25*x + 36, x^41 + 76*x^39 + 80*x^38 + 46*x^37 + 64*x^36 + 12*x^35 + 80*x^34 + 29*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 46*x^5 + 64*x^4 + 108*x^3 + 80*x^2 + 49*x + 32, x^41 + 76*x^39 + 56*x^38 + 78*x^37 + 56*x^36 + 76*x^35 + 40*x^34 + 61*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 78*x^5 + 120*x^4 + 44*x^3 + 104*x^2 + 81*x + 40, x^41 + 76*x^39 + 124*x^38 + 38*x^37 + 68*x^36 + 28*x^35 + 100*x^34 + 85*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 102*x^5 + 100*x^4 + 124*x^3 + 68*x^2 + 41*x + 124, x^41 + 76*x^39 + 108*x^38 + 118*x^37 + 100*x^36 + 60*x^35 + 84*x^34 + 101*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 54*x^5 + 4*x^4 + 28*x^3 + 52*x^2 + 57*x + 124, x^41 + 76*x^39 + 68*x^38 + 22*x^37 + 108*x^36 + 124*x^35 + 124*x^34 + 5*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 86*x^5 + 76*x^4 + 92*x^3 + 28*x^2 + 89*x + 52, x^41 + 76*x^39 + 64*x^38 + 110*x^37 + 80*x^36 + 12*x^35 + 96*x^34 + 93*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 110*x^5 + 80*x^4 + 108*x^3 + 96*x^2 + 113*x + 16, x^41 + 76*x^39 + 24*x^38 + 46*x^37 + 88*x^36 + 76*x^35 + 8*x^34 + 93*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 46*x^5 + 24*x^4 + 44*x^3 + 72*x^2 + 113*x + 72, x^41 + 76*x^39 + 112*x^38 + 110*x^37 + 12*x^35 + 112*x^34 + 93*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 110*x^5 + 108*x^3 + 112*x^2 + 113*x + 32, x^41 + 76*x^39 + 60*x^38 + 86*x^37 + 52*x^36 + 60*x^35 + 4*x^34 + 5*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 22*x^5 + 84*x^4 + 28*x^3 + 100*x^2 + 89*x + 44, x^41 + 76*x^39 + 88*x^38 + 46*x^37 + 88*x^36 + 12*x^35 + 8*x^34 + 29*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 46*x^5 + 24*x^4 + 108*x^3 + 72*x^2 + 49*x + 8, x^41 + 76*x^39 + 32*x^38 + 94*x^37 + 32*x^36 + 44*x^35 + 96*x^34 + 77*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 94*x^5 + 32*x^4 + 12*x^3 + 96*x^2 + 97*x + 96, x^41 + 76*x^39 + 32*x^38 + 14*x^37 + 112*x^36 + 12*x^35 + 64*x^34 + 61*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 14*x^5 + 112*x^4 + 108*x^3 + 64*x^2 + 81*x + 48, x^41 + 76*x^39 + 16*x^38 + 14*x^37 + 96*x^36 + 76*x^35 + 80*x^34 + 125*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 14*x^5 + 96*x^4 + 44*x^3 + 80*x^2 + 17*x + 64, x^41 + 76*x^39 + 124*x^38 + 22*x^37 + 20*x^36 + 124*x^35 + 68*x^34 + 5*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 86*x^5 + 52*x^4 + 92*x^3 + 36*x^2 + 89*x + 76, x^41 + 76*x^39 + 12*x^38 + 22*x^37 + 68*x^36 + 124*x^35 + 52*x^34 + 5*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 86*x^5 + 100*x^4 + 92*x^3 + 20*x^2 + 89*x + 28, x^41 + 76*x^39 + 100*x^38 + 102*x^37 + 92*x^36 + 28*x^35 + 60*x^34 + 21*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 38*x^5 + 60*x^4 + 124*x^3 + 92*x^2 + 105*x + 100, x^41 + 76*x^39 + 108*x^38 + 86*x^37 + 4*x^36 + 124*x^35 + 20*x^34 + 69*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 22*x^5 + 36*x^4 + 92*x^3 + 116*x^2 + 25*x + 28, x^41 + 76*x^39 + 120*x^38 + 14*x^37 + 88*x^36 + 12*x^35 + 104*x^34 + 61*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 14*x^5 + 24*x^4 + 108*x^3 + 40*x^2 + 81*x + 8, x^41 + 76*x^39 + 8*x^38 + 94*x^37 + 56*x^36 + 108*x^35 + 56*x^34 + 13*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 94*x^5 + 120*x^4 + 76*x^3 + 120*x^2 + 33*x + 72, x^41 + 76*x^39 + 16*x^38 + 62*x^37 + 16*x^36 + 44*x^35 + 112*x^34 + 109*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 62*x^5 + 16*x^4 + 12*x^3 + 112*x^2 + x + 112, x^41 + 76*x^39 + 108*x^38 + 6*x^37 + 116*x^36 + 28*x^35 + 116*x^34 + 117*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 70*x^5 + 20*x^4 + 124*x^3 + 84*x^2 + 73*x + 76, x^41 + 76*x^39 + 124*x^38 + 6*x^37 + 36*x^36 + 92*x^35 + 36*x^34 + 53*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 70*x^5 + 68*x^4 + 60*x^3 + 4*x^2 + 9*x + 92, x^41 + 76*x^39 + 44*x^38 + 70*x^37 + 20*x^36 + 92*x^35 + 52*x^34 + 117*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 6*x^5 + 52*x^4 + 60*x^3 + 20*x^2 + 73*x + 44, x^41 + 76*x^39 + 60*x^38 + 6*x^37 + 36*x^36 + 28*x^35 + 36*x^34 + 117*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 70*x^5 + 68*x^4 + 124*x^3 + 4*x^2 + 73*x + 28, x^41 + 76*x^39 + 60*x^38 + 70*x^37 + 36*x^36 + 28*x^35 + 36*x^34 + 53*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 6*x^5 + 68*x^4 + 124*x^3 + 4*x^2 + 9*x + 28, x^41 + 76*x^39 + 20*x^38 + 54*x^37 + 60*x^36 + 60*x^35 + 108*x^34 + 37*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 118*x^5 + 28*x^4 + 28*x^3 + 12*x^2 + 121*x + 36, x^41 + 76*x^39 + 60*x^38 + 102*x^37 + 36*x^36 + 28*x^35 + 100*x^34 + 21*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 38*x^5 + 68*x^4 + 124*x^3 + 68*x^2 + 105*x + 92, x^41 + 76*x^39 + 120*x^38 + 110*x^37 + 24*x^36 + 12*x^35 + 40*x^34 + 93*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 110*x^5 + 88*x^4 + 108*x^3 + 104*x^2 + 113*x + 8, x^41 + 76*x^39 + 72*x^38 + 126*x^37 + 56*x^36 + 44*x^35 + 120*x^34 + 45*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 126*x^5 + 120*x^4 + 12*x^3 + 56*x^2 + 65*x + 72, x^41 + 76*x^39 + 24*x^38 + 62*x^37 + 104*x^36 + 108*x^35 + 104*x^34 + 45*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 62*x^5 + 40*x^4 + 76*x^3 + 40*x^2 + 65*x + 88, x^41 + 76*x^39 + 84*x^38 + 22*x^37 + 92*x^36 + 60*x^35 + 44*x^34 + 69*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 86*x^5 + 60*x^4 + 28*x^3 + 76*x^2 + 25*x + 4, x^41 + 76*x^39 + 4*x^38 + 70*x^37 + 60*x^36 + 28*x^35 + 92*x^34 + 53*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 6*x^5 + 28*x^4 + 124*x^3 + 124*x^2 + 9*x + 68, x^41 + 76*x^39 + 52*x^38 + 38*x^37 + 12*x^36 + 28*x^35 + 108*x^34 + 85*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 102*x^5 + 108*x^4 + 124*x^3 + 12*x^2 + 41*x + 52, x^41 + 76*x^39 + 24*x^38 + 126*x^37 + 72*x^36 + 44*x^35 + 104*x^34 + 45*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 126*x^5 + 8*x^4 + 12*x^3 + 40*x^2 + 65*x + 120, x^41 + 76*x^39 + 64*x^38 + 94*x^37 + 64*x^36 + 44*x^35 + 64*x^34 + 77*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 94*x^5 + 64*x^4 + 12*x^3 + 64*x^2 + 97*x + 64, x^41 + 76*x^39 + 52*x^38 + 38*x^37 + 44*x^36 + 28*x^35 + 44*x^34 + 85*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 102*x^5 + 12*x^4 + 124*x^3 + 76*x^2 + 41*x + 84, x^41 + 76*x^39 + 72*x^38 + 78*x^37 + 8*x^36 + 76*x^35 + 88*x^34 + 61*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 78*x^5 + 72*x^4 + 44*x^3 + 24*x^2 + 81*x + 24, x^41 + 76*x^39 + 88*x^38 + 110*x^37 + 88*x^36 + 12*x^35 + 8*x^34 + 93*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 110*x^5 + 24*x^4 + 108*x^3 + 72*x^2 + 113*x + 8, x^41 + 76*x^39 + 112*x^38 + 62*x^37 + 80*x^36 + 108*x^35 + 16*x^34 + 45*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 62*x^5 + 80*x^4 + 76*x^3 + 16*x^2 + 65*x + 48, x^41 + 76*x^39 + 116*x^38 + 102*x^37 + 44*x^36 + 92*x^35 + 44*x^34 + 85*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 38*x^5 + 12*x^4 + 60*x^3 + 76*x^2 + 41*x + 20, x^41 + 76*x^39 + 80*x^38 + 78*x^37 + 64*x^36 + 12*x^35 + 16*x^34 + 125*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 78*x^5 + 64*x^4 + 108*x^3 + 16*x^2 + 17*x + 96, x^41 + 76*x^39 + 44*x^38 + 38*x^37 + 52*x^36 + 92*x^35 + 52*x^34 + 21*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 102*x^5 + 84*x^4 + 60*x^3 + 20*x^2 + 105*x + 12, x^41 + 76*x^39 + 60*x^38 + 22*x^37 + 116*x^36 + 60*x^35 + 4*x^34 + 69*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 86*x^5 + 20*x^4 + 28*x^3 + 100*x^2 + 25*x + 108, x^41 + 76*x^39 + 12*x^38 + 86*x^37 + 4*x^36 + 124*x^35 + 52*x^34 + 69*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 22*x^5 + 36*x^4 + 92*x^3 + 20*x^2 + 25*x + 92, x^41 + 76*x^39 + 60*x^38 + 102*x^37 + 68*x^36 + 92*x^35 + 100*x^34 + 85*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 38*x^5 + 100*x^4 + 60*x^3 + 68*x^2 + 41*x + 60, x^41 + 76*x^39 + 80*x^38 + 62*x^37 + 16*x^36 + 108*x^35 + 112*x^34 + 45*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 62*x^5 + 16*x^4 + 76*x^3 + 112*x^2 + 65*x + 48, x^41 + 76*x^39 + 108*x^38 + 86*x^37 + 68*x^36 + 124*x^35 + 20*x^34 + 69*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 22*x^5 + 100*x^4 + 92*x^3 + 116*x^2 + 25*x + 92, x^41 + 76*x^39 + 64*x^38 + 126*x^37 + 32*x^36 + 108*x^35 + 109*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 126*x^5 + 32*x^4 + 76*x^3 + x + 32, x^41 + 76*x^39 + 40*x^38 + 78*x^37 + 72*x^36 + 12*x^35 + 120*x^34 + 125*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 78*x^5 + 8*x^4 + 108*x^3 + 56*x^2 + 17*x + 88, x^41 + 76*x^39 + 4*x^38 + 38*x^37 + 28*x^36 + 28*x^35 + 92*x^34 + 85*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 102*x^5 + 124*x^4 + 124*x^3 + 124*x^2 + 41*x + 100, x^41 + 76*x^39 + 116*x^38 + 54*x^37 + 124*x^36 + 124*x^35 + 12*x^34 + 101*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 118*x^5 + 92*x^4 + 92*x^3 + 44*x^2 + 57*x + 100, x^41 + 76*x^39 + 120*x^38 + 110*x^37 + 120*x^36 + 76*x^35 + 40*x^34 + 29*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 110*x^5 + 56*x^4 + 44*x^3 + 104*x^2 + 49*x + 40, x^41 + 76*x^39 + 96*x^38 + 14*x^37 + 112*x^36 + 76*x^35 + 64*x^34 + 125*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 14*x^5 + 112*x^4 + 44*x^3 + 64*x^2 + 17*x + 112, x^41 + 76*x^39 + 120*x^38 + 62*x^37 + 72*x^36 + 44*x^35 + 72*x^34 + 109*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 62*x^5 + 8*x^4 + 12*x^3 + 8*x^2 + x + 56, x^41 + 76*x^39 + 116*x^38 + 86*x^37 + 124*x^36 + 124*x^35 + 76*x^34 + 69*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 22*x^5 + 92*x^4 + 92*x^3 + 108*x^2 + 25*x + 36, x^41 + 76*x^39 + 72*x^38 + 78*x^37 + 72*x^36 + 12*x^35 + 24*x^34 + 125*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 78*x^5 + 8*x^4 + 108*x^3 + 88*x^2 + 17*x + 24, x^41 + 76*x^39 + 16*x^38 + 14*x^37 + 96*x^36 + 12*x^35 + 16*x^34 + 61*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 14*x^5 + 96*x^4 + 108*x^3 + 16*x^2 + 81*x, x^41 + 76*x^39 + 48*x^38 + 110*x^37 + 32*x^36 + 12*x^35 + 112*x^34 + 93*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 110*x^5 + 32*x^4 + 108*x^3 + 112*x^2 + 113*x + 64, x^41 + 76*x^39 + 56*x^38 + 78*x^37 + 120*x^36 + 12*x^35 + 104*x^34 + 125*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 78*x^5 + 56*x^4 + 108*x^3 + 40*x^2 + 17*x + 40, x^41 + 76*x^39 + 104*x^38 + 94*x^37 + 120*x^36 + 108*x^35 + 24*x^34 + 13*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 94*x^5 + 56*x^4 + 76*x^3 + 88*x^2 + 33*x + 72, x^41 + 76*x^39 + 112*x^38 + 14*x^37 + 32*x^36 + 76*x^35 + 48*x^34 + 125*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 14*x^5 + 32*x^4 + 44*x^3 + 48*x^2 + 17*x + 64, x^41 + 76*x^39 + 108*x^38 + 70*x^37 + 116*x^36 + 28*x^35 + 116*x^34 + 53*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 6*x^5 + 20*x^4 + 124*x^3 + 84*x^2 + 9*x + 76, x^41 + 76*x^39 + 120*x^38 + 94*x^37 + 72*x^36 + 44*x^35 + 8*x^34 + 77*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 94*x^5 + 8*x^4 + 12*x^3 + 72*x^2 + 97*x + 120, x^41 + 76*x^39 + 76*x^38 + 22*x^37 + 68*x^36 + 60*x^35 + 52*x^34 + 69*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 86*x^5 + 100*x^4 + 28*x^3 + 20*x^2 + 25*x + 92, x^41 + 76*x^39 + 8*x^38 + 78*x^37 + 40*x^36 + 12*x^35 + 24*x^34 + 125*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 78*x^5 + 104*x^4 + 108*x^3 + 88*x^2 + 17*x + 120, x^41 + 76*x^39 + 104*x^38 + 94*x^37 + 56*x^36 + 44*x^35 + 88*x^34 + 77*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 94*x^5 + 120*x^4 + 12*x^3 + 24*x^2 + 97*x + 72, x^41 + 76*x^39 + 36*x^38 + 22*x^37 + 12*x^36 + 124*x^35 + 28*x^34 + 5*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 86*x^5 + 108*x^4 + 92*x^3 + 60*x^2 + 89*x + 20, x^41 + 76*x^39 + 116*x^38 + 22*x^37 + 92*x^36 + 124*x^35 + 12*x^34 + 5*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 86*x^5 + 60*x^4 + 92*x^3 + 44*x^2 + 89*x + 4, x^41 + 76*x^39 + 64*x^38 + 14*x^37 + 16*x^36 + 12*x^35 + 32*x^34 + 61*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 14*x^5 + 16*x^4 + 108*x^3 + 32*x^2 + 81*x + 16, x^41 + 76*x^39 + 120*x^38 + 30*x^37 + 104*x^36 + 44*x^35 + 72*x^34 + 13*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 30*x^5 + 40*x^4 + 12*x^3 + 8*x^2 + 33*x + 24, x^41 + 76*x^39 + 52*x^38 + 54*x^37 + 60*x^36 + 124*x^35 + 76*x^34 + 101*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 118*x^5 + 28*x^4 + 92*x^3 + 108*x^2 + 57*x + 36, x^41 + 76*x^39 + 80*x^38 + 46*x^37 + 32*x^36 + 12*x^35 + 16*x^34 + 29*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 46*x^5 + 32*x^4 + 108*x^3 + 16*x^2 + 49*x, x^41 + 76*x^39 + 52*x^38 + 118*x^37 + 92*x^36 + 124*x^35 + 12*x^34 + 37*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 54*x^5 + 60*x^4 + 92*x^3 + 44*x^2 + 121*x + 68, x^41 + 76*x^39 + 72*x^38 + 30*x^37 + 120*x^36 + 44*x^35 + 56*x^34 + 13*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 30*x^5 + 56*x^4 + 12*x^3 + 120*x^2 + 33*x + 72, x^41 + 76*x^39 + 62*x^37 + 96*x^36 + 108*x^35 + 64*x^34 + 45*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 62*x^5 + 96*x^4 + 76*x^3 + 64*x^2 + 65*x + 96, x^41 + 76*x^39 + 8*x^38 + 126*x^37 + 120*x^36 + 108*x^35 + 120*x^34 + 109*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 126*x^5 + 56*x^4 + 76*x^3 + 56*x^2 + x + 72, x^41 + 76*x^39 + 8*x^38 + 78*x^37 + 72*x^36 + 76*x^35 + 24*x^34 + 61*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 78*x^5 + 8*x^4 + 44*x^3 + 88*x^2 + 81*x + 88, x^41 + 76*x^39 + 72*x^38 + 62*x^37 + 88*x^36 + 108*x^35 + 120*x^34 + 45*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 62*x^5 + 24*x^4 + 76*x^3 + 56*x^2 + 65*x + 40, x^41 + 76*x^39 + 12*x^38 + 38*x^37 + 20*x^36 + 28*x^35 + 20*x^34 + 85*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 102*x^5 + 52*x^4 + 124*x^3 + 116*x^2 + 41*x + 108, x^41 + 76*x^39 + 40*x^38 + 14*x^37 + 40*x^36 + 76*x^35 + 120*x^34 + 125*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 14*x^5 + 104*x^4 + 44*x^3 + 56*x^2 + 17*x + 120, x^41 + 76*x^39 + 48*x^38 + 62*x^37 + 48*x^36 + 108*x^35 + 16*x^34 + 45*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 62*x^5 + 48*x^4 + 76*x^3 + 16*x^2 + 65*x + 16, x^41 + 76*x^39 + 92*x^38 + 6*x^37 + 68*x^36 + 28*x^35 + 4*x^34 + 117*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 70*x^5 + 100*x^4 + 124*x^3 + 100*x^2 + 73*x + 124, x^41 + 76*x^39 + 108*x^38 + 70*x^37 + 20*x^36 + 92*x^35 + 116*x^34 + 117*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 6*x^5 + 52*x^4 + 60*x^3 + 84*x^2 + 73*x + 44, x^41 + 76*x^39 + 84*x^38 + 70*x^37 + 108*x^36 + 92*x^35 + 76*x^34 + 117*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 6*x^5 + 76*x^4 + 60*x^3 + 108*x^2 + 73*x + 84, x^41 + 76*x^39 + 84*x^38 + 6*x^37 + 108*x^36 + 92*x^35 + 76*x^34 + 53*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 70*x^5 + 76*x^4 + 60*x^3 + 108*x^2 + 9*x + 84, x^41 + 76*x^39 + 116*x^38 + 86*x^37 + 92*x^36 + 124*x^35 + 12*x^34 + 69*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 22*x^5 + 60*x^4 + 92*x^3 + 44*x^2 + 25*x + 4, x^41 + 76*x^39 + 72*x^38 + 94*x^37 + 56*x^36 + 108*x^35 + 120*x^34 + 13*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 94*x^5 + 120*x^4 + 76*x^3 + 56*x^2 + 33*x + 72, x^41 + 76*x^39 + 68*x^38 + 38*x^37 + 60*x^36 + 28*x^35 + 92*x^34 + 85*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 102*x^5 + 28*x^4 + 124*x^3 + 124*x^2 + 41*x + 4, x^41 + 76*x^39 + 116*x^38 + 118*x^37 + 60*x^36 + 60*x^35 + 76*x^34 + 101*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 54*x^5 + 28*x^4 + 28*x^3 + 108*x^2 + 57*x + 100, x^41 + 76*x^39 + 16*x^38 + 14*x^37 + 12*x^35 + 80*x^34 + 61*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 14*x^5 + 108*x^3 + 80*x^2 + 81*x + 32, x^41 + 76*x^39 + 36*x^38 + 70*x^37 + 60*x^36 + 28*x^35 + 124*x^34 + 53*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 6*x^5 + 28*x^4 + 124*x^3 + 28*x^2 + 9*x + 4, x^41 + 76*x^39 + 24*x^38 + 78*x^37 + 24*x^36 + 76*x^35 + 72*x^34 + 61*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 78*x^5 + 88*x^4 + 44*x^3 + 8*x^2 + 81*x + 72, x^41 + 76*x^39 + 92*x^38 + 86*x^37 + 84*x^36 + 60*x^35 + 100*x^34 + 5*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 22*x^5 + 116*x^4 + 28*x^3 + 68*x^2 + 89*x + 12, x^41 + 76*x^39 + 60*x^38 + 118*x^37 + 20*x^36 + 60*x^35 + 4*x^34 + 101*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 54*x^5 + 52*x^4 + 28*x^3 + 100*x^2 + 57*x + 76, x^41 + 76*x^39 + 24*x^38 + 14*x^37 + 56*x^36 + 12*x^35 + 72*x^34 + 61*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 14*x^5 + 120*x^4 + 108*x^3 + 8*x^2 + 81*x + 40, x^41 + 76*x^39 + 56*x^38 + 14*x^37 + 24*x^36 + 12*x^35 + 40*x^34 + 61*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 14*x^5 + 88*x^4 + 108*x^3 + 104*x^2 + 81*x + 72, x^41 + 76*x^39 + 80*x^38 + 110*x^37 + 64*x^36 + 76*x^35 + 16*x^34 + 29*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 110*x^5 + 64*x^4 + 44*x^3 + 16*x^2 + 49*x + 96, x^41 + 76*x^39 + 104*x^38 + 94*x^37 + 56*x^36 + 108*x^35 + 24*x^34 + 13*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 94*x^5 + 120*x^4 + 76*x^3 + 88*x^2 + 33*x + 8, x^41 + 76*x^39 + 84*x^38 + 54*x^37 + 92*x^36 + 124*x^35 + 44*x^34 + 101*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 118*x^5 + 60*x^4 + 92*x^3 + 76*x^2 + 57*x + 4, x^41 + 76*x^39 + 60*x^38 + 38*x^37 + 4*x^36 + 92*x^35 + 100*x^34 + 21*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 102*x^5 + 36*x^4 + 60*x^3 + 68*x^2 + 105*x + 124, x^41 + 76*x^39 + 8*x^38 + 46*x^37 + 40*x^36 + 76*x^35 + 24*x^34 + 93*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 46*x^5 + 104*x^4 + 44*x^3 + 88*x^2 + 113*x + 120, x^41 + 76*x^39 + 28*x^38 + 54*x^37 + 52*x^36 + 124*x^35 + 100*x^34 + 101*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 118*x^5 + 84*x^4 + 92*x^3 + 68*x^2 + 57*x + 108, x^41 + 76*x^39 + 108*x^38 + 54*x^37 + 4*x^36 + 60*x^35 + 20*x^34 + 37*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 118*x^5 + 36*x^4 + 28*x^3 + 116*x^2 + 121*x + 28, x^41 + 76*x^39 + 32*x^38 + 62*x^37 + 96*x^36 + 44*x^35 + 32*x^34 + 109*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 62*x^5 + 96*x^4 + 12*x^3 + 32*x^2 + x + 96, x^41 + 76*x^39 + 112*x^38 + 126*x^37 + 16*x^36 + 44*x^35 + 80*x^34 + 45*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 126*x^5 + 16*x^4 + 12*x^3 + 80*x^2 + 65*x + 48, x^41 + 76*x^39 + 40*x^38 + 78*x^37 + 8*x^36 + 76*x^35 + 56*x^34 + 61*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 78*x^5 + 72*x^4 + 44*x^3 + 120*x^2 + 81*x + 88, x^41 + 76*x^39 + 84*x^38 + 118*x^37 + 28*x^36 + 60*x^35 + 108*x^34 + 101*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 54*x^5 + 124*x^4 + 28*x^3 + 12*x^2 + 57*x + 4, x^41 + 76*x^39 + 120*x^38 + 30*x^37 + 40*x^36 + 44*x^35 + 72*x^34 + 13*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 30*x^5 + 104*x^4 + 12*x^3 + 8*x^2 + 33*x + 88, x^41 + 76*x^39 + 64*x^38 + 14*x^37 + 16*x^36 + 76*x^35 + 96*x^34 + 125*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 14*x^5 + 16*x^4 + 44*x^3 + 96*x^2 + 17*x + 80, x^41 + 76*x^39 + 116*x^38 + 22*x^37 + 124*x^36 + 124*x^35 + 76*x^34 + 5*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 86*x^5 + 92*x^4 + 92*x^3 + 108*x^2 + 89*x + 36, x^41 + 76*x^39 + 48*x^38 + 14*x^37 + 12*x^35 + 112*x^34 + 61*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 14*x^5 + 108*x^3 + 112*x^2 + 81*x + 96, x^41 + 76*x^39 + 120*x^38 + 126*x^37 + 40*x^36 + 108*x^35 + 72*x^34 + 109*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 126*x^5 + 104*x^4 + 76*x^3 + 8*x^2 + x + 88, x^41 + 76*x^39 + 92*x^38 + 118*x^37 + 116*x^36 + 124*x^35 + 36*x^34 + 37*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 54*x^5 + 20*x^4 + 92*x^3 + 4*x^2 + 121*x + 44, x^41 + 76*x^39 + 16*x^38 + 126*x^37 + 48*x^36 + 108*x^35 + 112*x^34 + 109*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 126*x^5 + 48*x^4 + 76*x^3 + 112*x^2 + x + 80, x^41 + 76*x^39 + 8*x^38 + 78*x^37 + 8*x^36 + 76*x^35 + 24*x^34 + 61*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 78*x^5 + 72*x^4 + 44*x^3 + 88*x^2 + 81*x + 24, x^41 + 76*x^39 + 120*x^38 + 78*x^37 + 56*x^36 + 76*x^35 + 104*x^34 + 61*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 78*x^5 + 120*x^4 + 44*x^3 + 40*x^2 + 81*x + 40, x^41 + 76*x^39 + 16*x^38 + 14*x^37 + 64*x^36 + 76*x^35 + 16*x^34 + 125*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 14*x^5 + 64*x^4 + 44*x^3 + 16*x^2 + 17*x + 32, x^41 + 76*x^39 + 40*x^38 + 62*x^37 + 24*x^36 + 108*x^35 + 88*x^34 + 45*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 62*x^5 + 88*x^4 + 76*x^3 + 24*x^2 + 65*x + 40, x^41 + 76*x^39 + 68*x^38 + 118*x^37 + 12*x^36 + 60*x^35 + 60*x^34 + 101*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 54*x^5 + 108*x^4 + 28*x^3 + 92*x^2 + 57*x + 84, x^41 + 76*x^39 + 12*x^38 + 70*x^37 + 52*x^36 + 28*x^35 + 20*x^34 + 53*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 6*x^5 + 84*x^4 + 124*x^3 + 116*x^2 + 9*x + 76, x^41 + 76*x^39 + 24*x^38 + 94*x^37 + 72*x^36 + 108*x^35 + 104*x^34 + 13*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 94*x^5 + 8*x^4 + 76*x^3 + 40*x^2 + 33*x + 120, x^41 + 76*x^39 + 12*x^38 + 22*x^37 + 36*x^36 + 60*x^35 + 52*x^34 + 69*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 86*x^5 + 68*x^4 + 28*x^3 + 20*x^2 + 25*x + 60, x^41 + 76*x^39 + 48*x^38 + 94*x^37 + 80*x^36 + 108*x^35 + 16*x^34 + 13*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 94*x^5 + 80*x^4 + 76*x^3 + 16*x^2 + 33*x + 112, x^41 + 76*x^39 + 36*x^38 + 86*x^37 + 76*x^36 + 60*x^35 + 92*x^34 + 5*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 22*x^5 + 44*x^4 + 28*x^3 + 124*x^2 + 89*x + 20, x^41 + 76*x^39 + 68*x^38 + 102*x^37 + 28*x^36 + 28*x^35 + 28*x^34 + 21*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 38*x^5 + 124*x^4 + 124*x^3 + 60*x^2 + 105*x + 100, x^41 + 76*x^39 + 36*x^38 + 54*x^37 + 12*x^36 + 124*x^35 + 92*x^34 + 101*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 118*x^5 + 108*x^4 + 92*x^3 + 124*x^2 + 57*x + 84, x^41 + 76*x^39 + 108*x^38 + 54*x^37 + 68*x^36 + 60*x^35 + 20*x^34 + 37*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 118*x^5 + 100*x^4 + 28*x^3 + 116*x^2 + 121*x + 92, x^41 + 76*x^39 + 20*x^38 + 118*x^37 + 92*x^36 + 60*x^35 + 44*x^34 + 101*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 54*x^5 + 60*x^4 + 28*x^3 + 76*x^2 + 57*x + 68, x^41 + 76*x^39 + 84*x^38 + 38*x^37 + 12*x^36 + 92*x^35 + 76*x^34 + 21*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 102*x^5 + 108*x^4 + 60*x^3 + 108*x^2 + 105*x + 52, x^41 + 76*x^39 + 108*x^38 + 22*x^37 + 68*x^36 + 60*x^35 + 84*x^34 + 69*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 86*x^5 + 100*x^4 + 28*x^3 + 52*x^2 + 25*x + 28, x^41 + 76*x^39 + 96*x^38 + 46*x^37 + 80*x^36 + 12*x^35 + 29*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 46*x^5 + 80*x^4 + 108*x^3 + 49*x + 80, x^41 + 76*x^39 + 68*x^38 + 86*x^37 + 108*x^36 + 60*x^35 + 60*x^34 + 5*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 22*x^5 + 76*x^4 + 28*x^3 + 92*x^2 + 89*x + 116, x^41 + 76*x^39 + 48*x^38 + 46*x^37 + 76*x^35 + 112*x^34 + 93*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 46*x^5 + 44*x^3 + 112*x^2 + 113*x + 96, x^41 + 76*x^39 + 88*x^38 + 110*x^37 + 88*x^36 + 76*x^35 + 72*x^34 + 29*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 110*x^5 + 24*x^4 + 44*x^3 + 8*x^2 + 49*x + 72, x^41 + 76*x^39 + 112*x^38 + 46*x^37 + 96*x^36 + 76*x^35 + 112*x^34 + 93*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 46*x^5 + 96*x^4 + 44*x^3 + 112*x^2 + 113*x + 64, x^41 + 76*x^39 + 116*x^38 + 54*x^37 + 124*x^36 + 60*x^35 + 76*x^34 + 37*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 118*x^5 + 92*x^4 + 28*x^3 + 108*x^2 + 121*x + 36, x^41 + 76*x^39 + 16*x^38 + 126*x^37 + 48*x^36 + 44*x^35 + 48*x^34 + 45*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 126*x^5 + 48*x^4 + 12*x^3 + 48*x^2 + 65*x + 16, x^41 + 76*x^39 + 76*x^38 + 102*x^37 + 52*x^36 + 28*x^35 + 20*x^34 + 21*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 38*x^5 + 84*x^4 + 124*x^3 + 116*x^2 + 105*x + 12, x^41 + 76*x^39 + 60*x^38 + 118*x^37 + 20*x^36 + 124*x^35 + 68*x^34 + 37*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 54*x^5 + 52*x^4 + 92*x^3 + 36*x^2 + 121*x + 12, x^41 + 76*x^39 + 44*x^38 + 86*x^37 + 4*x^36 + 124*x^35 + 84*x^34 + 69*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 22*x^5 + 36*x^4 + 92*x^3 + 52*x^2 + 25*x + 28, x^41 + 76*x^39 + 24*x^38 + 94*x^37 + 72*x^36 + 44*x^35 + 40*x^34 + 77*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 94*x^5 + 8*x^4 + 12*x^3 + 104*x^2 + 97*x + 56, x^41 + 76*x^39 + 24*x^38 + 110*x^37 + 56*x^36 + 12*x^35 + 8*x^34 + 93*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 110*x^5 + 120*x^4 + 108*x^3 + 72*x^2 + 113*x + 104, x^41 + 76*x^39 + 116*x^38 + 22*x^37 + 28*x^36 + 124*x^35 + 12*x^34 + 5*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 86*x^5 + 124*x^4 + 92*x^3 + 44*x^2 + 89*x + 68, x^41 + 76*x^39 + 64*x^38 + 14*x^37 + 80*x^36 + 76*x^35 + 96*x^34 + 125*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 14*x^5 + 80*x^4 + 44*x^3 + 96*x^2 + 17*x + 16, x^41 + 76*x^39 + 4*x^38 + 38*x^37 + 124*x^36 + 92*x^35 + 92*x^34 + 21*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 102*x^5 + 92*x^4 + 60*x^3 + 124*x^2 + 105*x + 4, x^41 + 76*x^39 + 14*x^37 + 48*x^36 + 12*x^35 + 32*x^34 + 61*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 14*x^5 + 48*x^4 + 108*x^3 + 32*x^2 + 81*x + 48, x^41 + 76*x^39 + 52*x^38 + 70*x^37 + 108*x^36 + 28*x^35 + 108*x^34 + 53*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 6*x^5 + 76*x^4 + 124*x^3 + 12*x^2 + 9*x + 84, x^41 + 76*x^39 + 120*x^38 + 30*x^37 + 8*x^36 + 44*x^35 + 8*x^34 + 13*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 30*x^5 + 72*x^4 + 12*x^3 + 72*x^2 + 33*x + 56, x^41 + 76*x^39 + 44*x^38 + 38*x^37 + 20*x^36 + 28*x^35 + 52*x^34 + 85*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 102*x^5 + 52*x^4 + 124*x^3 + 20*x^2 + 41*x + 44, x^41 + 76*x^39 + 56*x^38 + 126*x^37 + 8*x^36 + 108*x^35 + 72*x^34 + 109*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 126*x^5 + 72*x^4 + 76*x^3 + 8*x^2 + x + 56, x^41 + 76*x^39 + 116*x^38 + 70*x^37 + 108*x^36 + 92*x^35 + 108*x^34 + 117*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 6*x^5 + 76*x^4 + 60*x^3 + 12*x^2 + 73*x + 20, x^41 + 76*x^39 + 36*x^38 + 86*x^37 + 76*x^36 + 124*x^35 + 28*x^34 + 69*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 22*x^5 + 44*x^4 + 92*x^3 + 60*x^2 + 25*x + 84, x^41 + 76*x^39 + 40*x^38 + 30*x^37 + 24*x^36 + 44*x^35 + 88*x^34 + 13*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 30*x^5 + 88*x^4 + 12*x^3 + 24*x^2 + 33*x + 40, x^41 + 76*x^39 + 80*x^38 + 30*x^37 + 112*x^36 + 44*x^35 + 48*x^34 + 13*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 30*x^5 + 112*x^4 + 12*x^3 + 48*x^2 + 33*x + 16, x^41 + 76*x^39 + 8*x^38 + 62*x^37 + 24*x^36 + 108*x^35 + 56*x^34 + 45*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 62*x^5 + 88*x^4 + 76*x^3 + 120*x^2 + 65*x + 104, x^41 + 76*x^39 + 12*x^38 + 118*x^37 + 100*x^36 + 60*x^35 + 116*x^34 + 101*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 54*x^5 + 4*x^4 + 28*x^3 + 84*x^2 + 57*x + 60, x^41 + 76*x^39 + 76*x^38 + 22*x^37 + 4*x^36 + 124*x^35 + 116*x^34 + 5*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 86*x^5 + 36*x^4 + 92*x^3 + 84*x^2 + 89*x + 92, x^41 + 76*x^39 + 108*x^38 + 22*x^37 + 36*x^36 + 60*x^35 + 20*x^34 + 69*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 86*x^5 + 68*x^4 + 28*x^3 + 116*x^2 + 25*x + 124, x^41 + 76*x^39 + 68*x^38 + 6*x^37 + 92*x^36 + 92*x^35 + 28*x^34 + 53*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 70*x^5 + 60*x^4 + 60*x^3 + 60*x^2 + 9*x + 36, x^41 + 76*x^39 + 16*x^38 + 30*x^37 + 80*x^36 + 44*x^35 + 48*x^34 + 13*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 30*x^5 + 80*x^4 + 12*x^3 + 48*x^2 + 33*x + 112, x^41 + 76*x^39 + 20*x^38 + 38*x^37 + 76*x^36 + 92*x^35 + 12*x^34 + 21*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 102*x^5 + 44*x^4 + 60*x^3 + 44*x^2 + 105*x + 116, x^41 + 76*x^39 + 16*x^38 + 62*x^37 + 48*x^36 + 108*x^35 + 112*x^34 + 45*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 62*x^5 + 48*x^4 + 76*x^3 + 112*x^2 + 65*x + 80, x^41 + 76*x^39 + 96*x^38 + 110*x^37 + 112*x^36 + 12*x^35 + 64*x^34 + 93*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 110*x^5 + 112*x^4 + 108*x^3 + 64*x^2 + 113*x + 112, x^41 + 76*x^39 + 116*x^38 + 54*x^37 + 92*x^36 + 60*x^35 + 12*x^34 + 37*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 118*x^5 + 60*x^4 + 28*x^3 + 44*x^2 + 121*x + 4, x^41 + 76*x^39 + 124*x^38 + 22*x^37 + 20*x^36 + 60*x^35 + 4*x^34 + 69*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 86*x^5 + 52*x^4 + 28*x^3 + 100*x^2 + 25*x + 12, x^41 + 76*x^39 + 36*x^38 + 22*x^37 + 108*x^36 + 124*x^35 + 92*x^34 + 5*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 86*x^5 + 76*x^4 + 92*x^3 + 124*x^2 + 89*x + 116, x^41 + 76*x^39 + 112*x^38 + 30*x^37 + 112*x^36 + 44*x^35 + 80*x^34 + 13*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 30*x^5 + 112*x^4 + 12*x^3 + 80*x^2 + 33*x + 80, x^41 + 76*x^39 + 24*x^38 + 110*x^37 + 24*x^36 + 76*x^35 + 8*x^34 + 29*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 110*x^5 + 88*x^4 + 44*x^3 + 72*x^2 + 49*x + 8, x^41 + 76*x^39 + 112*x^38 + 110*x^37 + 32*x^36 + 12*x^35 + 48*x^34 + 93*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 110*x^5 + 32*x^4 + 108*x^3 + 48*x^2 + 113*x + 64, x^41 + 76*x^39 + 76*x^38 + 38*x^37 + 84*x^36 + 92*x^35 + 20*x^34 + 21*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 102*x^5 + 116*x^4 + 60*x^3 + 116*x^2 + 105*x + 108, x^41 + 76*x^39 + 44*x^38 + 54*x^37 + 68*x^36 + 124*x^35 + 20*x^34 + 101*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 118*x^5 + 100*x^4 + 92*x^3 + 116*x^2 + 57*x + 28, x^41 + 76*x^39 + 4*x^38 + 102*x^37 + 60*x^36 + 28*x^35 + 28*x^34 + 21*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 38*x^5 + 28*x^4 + 124*x^3 + 60*x^2 + 105*x + 4, x^41 + 76*x^39 + 72*x^38 + 30*x^37 + 56*x^36 + 108*x^35 + 120*x^34 + 77*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 30*x^5 + 120*x^4 + 76*x^3 + 56*x^2 + 97*x + 72, x^41 + 76*x^39 + 116*x^38 + 54*x^37 + 92*x^36 + 124*x^35 + 76*x^34 + 101*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 118*x^5 + 60*x^4 + 92*x^3 + 108*x^2 + 57*x + 68, x^41 + 76*x^39 + 100*x^38 + 70*x^37 + 28*x^36 + 92*x^35 + 60*x^34 + 117*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 6*x^5 + 124*x^4 + 60*x^3 + 92*x^2 + 73*x + 36, x^41 + 76*x^39 + 14*x^37 + 48*x^36 + 76*x^35 + 96*x^34 + 125*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 14*x^5 + 48*x^4 + 44*x^3 + 96*x^2 + 17*x + 112, x^41 + 76*x^39 + 30*x^37 + 32*x^36 + 108*x^35 + 77*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 30*x^5 + 32*x^4 + 76*x^3 + 97*x + 96, x^41 + 76*x^39 + 92*x^38 + 118*x^37 + 52*x^36 + 124*x^35 + 36*x^34 + 37*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 54*x^5 + 84*x^4 + 92*x^3 + 4*x^2 + 121*x + 108, x^41 + 76*x^39 + 8*x^38 + 126*x^37 + 88*x^36 + 108*x^35 + 56*x^34 + 109*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 126*x^5 + 24*x^4 + 76*x^3 + 120*x^2 + x + 40, x^41 + 76*x^39 + 16*x^38 + 62*x^37 + 16*x^36 + 108*x^35 + 48*x^34 + 45*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 62*x^5 + 16*x^4 + 76*x^3 + 48*x^2 + 65*x + 48, x^41 + 76*x^39 + 52*x^38 + 102*x^37 + 12*x^36 + 28*x^35 + 108*x^34 + 21*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 38*x^5 + 108*x^4 + 124*x^3 + 12*x^2 + 105*x + 52, x^41 + 76*x^39 + 52*x^38 + 102*x^37 + 44*x^36 + 28*x^35 + 44*x^34 + 21*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 38*x^5 + 12*x^4 + 124*x^3 + 76*x^2 + 105*x + 84, x^41 + 76*x^39 + 104*x^38 + 94*x^37 + 88*x^36 + 108*x^35 + 88*x^34 + 13*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 94*x^5 + 24*x^4 + 76*x^3 + 24*x^2 + 33*x + 40, x^41 + 76*x^39 + 44*x^38 + 102*x^37 + 52*x^36 + 92*x^35 + 52*x^34 + 85*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 38*x^5 + 84*x^4 + 60*x^3 + 20*x^2 + 41*x + 12, x^41 + 76*x^39 + 8*x^38 + 78*x^37 + 8*x^36 + 12*x^35 + 88*x^34 + 125*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 78*x^5 + 72*x^4 + 108*x^3 + 24*x^2 + 17*x + 88, x^41 + 76*x^39 + 84*x^38 + 22*x^37 + 124*x^36 + 124*x^35 + 44*x^34 + 5*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 86*x^5 + 92*x^4 + 92*x^3 + 76*x^2 + 89*x + 100, x^41 + 76*x^39 + 88*x^38 + 46*x^37 + 88*x^36 + 76*x^35 + 72*x^34 + 93*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 46*x^5 + 24*x^4 + 44*x^3 + 8*x^2 + 113*x + 72, x^41 + 76*x^39 + 48*x^38 + 30*x^37 + 16*x^36 + 44*x^35 + 80*x^34 + 13*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 30*x^5 + 16*x^4 + 12*x^3 + 80*x^2 + 33*x + 112, x^41 + 76*x^39 + 20*x^38 + 70*x^37 + 44*x^36 + 28*x^35 + 76*x^34 + 53*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 6*x^5 + 12*x^4 + 124*x^3 + 108*x^2 + 9*x + 84, x^41 + 76*x^39 + 56*x^38 + 14*x^37 + 56*x^36 + 76*x^35 + 40*x^34 + 125*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 14*x^5 + 120*x^4 + 44*x^3 + 104*x^2 + 17*x + 40, x^41 + 76*x^39 + 44*x^38 + 6*x^37 + 116*x^36 + 28*x^35 + 52*x^34 + 117*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 70*x^5 + 20*x^4 + 124*x^3 + 20*x^2 + 73*x + 76, x^41 + 76*x^39 + 4*x^38 + 70*x^37 + 60*x^36 + 92*x^35 + 28*x^34 + 117*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 6*x^5 + 28*x^4 + 60*x^3 + 60*x^2 + 73*x + 4, x^41 + 76*x^39 + 88*x^38 + 78*x^37 + 56*x^36 + 12*x^35 + 8*x^34 + 125*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 78*x^5 + 120*x^4 + 108*x^3 + 72*x^2 + 17*x + 40, x^41 + 76*x^39 + 12*x^38 + 118*x^37 + 100*x^36 + 124*x^35 + 52*x^34 + 37*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 54*x^5 + 4*x^4 + 92*x^3 + 20*x^2 + 121*x + 124, x^41 + 76*x^39 + 112*x^38 + 46*x^37 + 12*x^35 + 112*x^34 + 29*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 46*x^5 + 108*x^3 + 112*x^2 + 49*x + 32, x^41 + 76*x^39 + 20*x^38 + 6*x^37 + 12*x^36 + 28*x^35 + 12*x^34 + 117*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 70*x^5 + 108*x^4 + 124*x^3 + 44*x^2 + 73*x + 52, x^41 + 76*x^39 + 52*x^38 + 86*x^37 + 28*x^36 + 124*x^35 + 76*x^34 + 69*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 22*x^5 + 124*x^4 + 92*x^3 + 108*x^2 + 25*x + 68, x^41 + 76*x^39 + 4*x^38 + 102*x^37 + 28*x^36 + 28*x^35 + 92*x^34 + 21*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 38*x^5 + 124*x^4 + 124*x^3 + 124*x^2 + 105*x + 100, x^41 + 76*x^39 + 44*x^38 + 118*x^37 + 36*x^36 + 60*x^35 + 20*x^34 + 101*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 54*x^5 + 68*x^4 + 28*x^3 + 116*x^2 + 57*x + 60, x^41 + 76*x^39 + 32*x^38 + 126*x^37 + 96*x^36 + 44*x^35 + 32*x^34 + 45*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 126*x^5 + 96*x^4 + 12*x^3 + 32*x^2 + 65*x + 96, x^41 + 76*x^39 + 28*x^38 + 70*x^37 + 4*x^36 + 92*x^35 + 4*x^34 + 117*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 6*x^5 + 36*x^4 + 60*x^3 + 100*x^2 + 73*x + 124, x^41 + 76*x^39 + 56*x^38 + 30*x^37 + 104*x^36 + 108*x^35 + 72*x^34 + 77*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 30*x^5 + 40*x^4 + 76*x^3 + 8*x^2 + 97*x + 88, x^41 + 76*x^39 + 64*x^38 + 94*x^37 + 44*x^35 + 64*x^34 + 77*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 94*x^5 + 12*x^3 + 64*x^2 + 97*x, x^41 + 76*x^39 + 84*x^38 + 102*x^37 + 44*x^36 + 28*x^35 + 76*x^34 + 21*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 38*x^5 + 12*x^4 + 124*x^3 + 108*x^2 + 105*x + 20, x^41 + 76*x^39 + 8*x^38 + 46*x^37 + 72*x^36 + 12*x^35 + 24*x^34 + 29*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 46*x^5 + 8*x^4 + 108*x^3 + 88*x^2 + 49*x + 88, x^41 + 76*x^39 + 80*x^38 + 30*x^37 + 48*x^36 + 108*x^35 + 112*x^34 + 77*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 30*x^5 + 48*x^4 + 76*x^3 + 112*x^2 + 97*x + 16, x^41 + 76*x^39 + 64*x^38 + 110*x^37 + 16*x^36 + 12*x^35 + 96*x^34 + 93*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 110*x^5 + 16*x^4 + 108*x^3 + 96*x^2 + 113*x + 80, x^41 + 76*x^39 + 100*x^38 + 70*x^37 + 124*x^36 + 28*x^35 + 60*x^34 + 53*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 6*x^5 + 92*x^4 + 124*x^3 + 92*x^2 + 9*x + 68, x^41 + 76*x^39 + 14*x^37 + 112*x^36 + 76*x^35 + 96*x^34 + 125*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 14*x^5 + 112*x^4 + 44*x^3 + 96*x^2 + 17*x + 48, x^41 + 76*x^39 + 60*x^38 + 22*x^37 + 116*x^36 + 124*x^35 + 68*x^34 + 5*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 86*x^5 + 20*x^4 + 92*x^3 + 36*x^2 + 89*x + 44, x^41 + 76*x^39 + 60*x^38 + 102*x^37 + 4*x^36 + 92*x^35 + 100*x^34 + 85*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 38*x^5 + 36*x^4 + 60*x^3 + 68*x^2 + 41*x + 124, x^41 + 76*x^39 + 4*x^38 + 54*x^37 + 12*x^36 + 124*x^35 + 60*x^34 + 101*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 118*x^5 + 108*x^4 + 92*x^3 + 92*x^2 + 57*x + 20, x^41 + 76*x^39 + 16*x^38 + 110*x^37 + 64*x^36 + 12*x^35 + 16*x^34 + 93*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 110*x^5 + 64*x^4 + 108*x^3 + 16*x^2 + 113*x + 32, x^41 + 76*x^39 + 88*x^38 + 46*x^37 + 120*x^36 + 76*x^35 + 8*x^34 + 93*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 46*x^5 + 56*x^4 + 44*x^3 + 72*x^2 + 113*x + 104, x^41 + 76*x^39 + 124*x^38 + 118*x^37 + 116*x^36 + 60*x^35 + 4*x^34 + 101*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 54*x^5 + 20*x^4 + 28*x^3 + 100*x^2 + 57*x + 44, x^41 + 76*x^39 + 120*x^38 + 126*x^37 + 40*x^36 + 44*x^35 + 8*x^34 + 45*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 126*x^5 + 104*x^4 + 12*x^3 + 72*x^2 + 65*x + 24, x^41 + 76*x^39 + 16*x^38 + 62*x^37 + 112*x^36 + 44*x^35 + 48*x^34 + 109*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 62*x^5 + 112*x^4 + 12*x^3 + 48*x^2 + x + 80, x^41 + 76*x^39 + 44*x^38 + 86*x^37 + 36*x^36 + 60*x^35 + 84*x^34 + 5*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 22*x^5 + 68*x^4 + 28*x^3 + 52*x^2 + 89*x + 124, x^41 + 76*x^39 + 36*x^38 + 54*x^37 + 76*x^36 + 60*x^35 + 28*x^34 + 37*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 118*x^5 + 44*x^4 + 28*x^3 + 60*x^2 + 121*x + 84, x^41 + 76*x^39 + 40*x^38 + 46*x^37 + 104*x^36 + 76*x^35 + 56*x^34 + 93*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 46*x^5 + 40*x^4 + 44*x^3 + 120*x^2 + 113*x + 120, x^41 + 76*x^39 + 52*x^38 + 70*x^37 + 12*x^36 + 28*x^35 + 44*x^34 + 53*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 6*x^5 + 108*x^4 + 124*x^3 + 76*x^2 + 9*x + 116, x^41 + 76*x^39 + 8*x^38 + 62*x^37 + 120*x^36 + 44*x^35 + 56*x^34 + 109*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 62*x^5 + 56*x^4 + 12*x^3 + 120*x^2 + x + 8, x^41 + 76*x^39 + 116*x^38 + 22*x^37 + 60*x^36 + 60*x^35 + 12*x^34 + 69*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 86*x^5 + 28*x^4 + 28*x^3 + 44*x^2 + 25*x + 36, x^41 + 76*x^39 + 104*x^38 + 62*x^37 + 24*x^36 + 44*x^35 + 88*x^34 + 109*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 62*x^5 + 88*x^4 + 12*x^3 + 24*x^2 + x + 104, x^41 + 76*x^39 + 20*x^38 + 22*x^37 + 60*x^36 + 60*x^35 + 44*x^34 + 69*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 86*x^5 + 28*x^4 + 28*x^3 + 76*x^2 + 25*x + 100, x^41 + 76*x^39 + 12*x^38 + 38*x^37 + 52*x^36 + 28*x^35 + 84*x^34 + 85*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 102*x^5 + 84*x^4 + 124*x^3 + 52*x^2 + 41*x + 12, x^41 + 76*x^39 + 100*x^38 + 86*x^37 + 44*x^36 + 124*x^35 + 28*x^34 + 69*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 22*x^5 + 12*x^4 + 92*x^3 + 60*x^2 + 25*x + 52, x^41 + 76*x^39 + 44*x^38 + 70*x^37 + 116*x^36 + 28*x^35 + 52*x^34 + 53*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 6*x^5 + 20*x^4 + 124*x^3 + 20*x^2 + 9*x + 76, x^41 + 76*x^39 + 124*x^38 + 38*x^37 + 36*x^36 + 28*x^35 + 36*x^34 + 85*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 102*x^5 + 68*x^4 + 124*x^3 + 4*x^2 + 41*x + 92, x^41 + 76*x^39 + 48*x^38 + 78*x^37 + 12*x^35 + 112*x^34 + 125*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 78*x^5 + 108*x^3 + 112*x^2 + 17*x + 96, x^41 + 76*x^39 + 68*x^38 + 54*x^37 + 44*x^36 + 124*x^35 + 60*x^34 + 101*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 118*x^5 + 12*x^4 + 92*x^3 + 92*x^2 + 57*x + 52, x^41 + 76*x^39 + 112*x^38 + 78*x^37 + 96*x^36 + 12*x^35 + 112*x^34 + 125*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 78*x^5 + 96*x^4 + 108*x^3 + 112*x^2 + 17*x + 64, x^41 + 76*x^39 + 84*x^38 + 118*x^37 + 60*x^36 + 60*x^35 + 44*x^34 + 101*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 54*x^5 + 28*x^4 + 28*x^3 + 76*x^2 + 57*x + 36, x^41 + 76*x^39 + 60*x^38 + 22*x^37 + 52*x^36 + 124*x^35 + 68*x^34 + 5*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 86*x^5 + 84*x^4 + 92*x^3 + 36*x^2 + 89*x + 108, x^41 + 76*x^39 + 24*x^38 + 46*x^37 + 56*x^36 + 12*x^35 + 8*x^34 + 29*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 46*x^5 + 120*x^4 + 108*x^3 + 72*x^2 + 49*x + 104, x^41 + 76*x^39 + 108*x^38 + 22*x^37 + 100*x^36 + 60*x^35 + 20*x^34 + 69*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 86*x^5 + 4*x^4 + 28*x^3 + 116*x^2 + 25*x + 60, x^41 + 76*x^39 + 72*x^38 + 78*x^37 + 72*x^36 + 76*x^35 + 88*x^34 + 61*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 78*x^5 + 8*x^4 + 44*x^3 + 24*x^2 + 81*x + 88, x^41 + 76*x^39 + 56*x^38 + 30*x^37 + 72*x^36 + 108*x^35 + 8*x^34 + 77*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 30*x^5 + 8*x^4 + 76*x^3 + 72*x^2 + 97*x + 56, x^41 + 76*x^39 + 84*x^38 + 54*x^37 + 92*x^36 + 60*x^35 + 108*x^34 + 37*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 118*x^5 + 60*x^4 + 28*x^3 + 12*x^2 + 121*x + 68, x^41 + 76*x^39 + 52*x^38 + 22*x^37 + 60*x^36 + 124*x^35 + 12*x^34 + 5*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 86*x^5 + 28*x^4 + 92*x^3 + 44*x^2 + 89*x + 100, x^41 + 76*x^39 + 64*x^38 + 14*x^37 + 80*x^36 + 12*x^35 + 32*x^34 + 61*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 14*x^5 + 80*x^4 + 108*x^3 + 32*x^2 + 81*x + 80, x^41 + 76*x^39 + 84*x^38 + 22*x^37 + 60*x^36 + 124*x^35 + 44*x^34 + 5*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 86*x^5 + 28*x^4 + 92*x^3 + 76*x^2 + 89*x + 36, x^41 + 76*x^39 + 40*x^38 + 94*x^37 + 24*x^36 + 44*x^35 + 88*x^34 + 77*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 94*x^5 + 88*x^4 + 12*x^3 + 24*x^2 + 97*x + 40, x^41 + 76*x^39 + 44*x^38 + 6*x^37 + 84*x^36 + 28*x^35 + 116*x^34 + 117*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 70*x^5 + 116*x^4 + 124*x^3 + 84*x^2 + 73*x + 44, x^41 + 76*x^39 + 116*x^38 + 102*x^37 + 12*x^36 + 92*x^35 + 108*x^34 + 85*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 38*x^5 + 108*x^4 + 60*x^3 + 12*x^2 + 41*x + 116, x^41 + 76*x^39 + 88*x^38 + 78*x^37 + 120*x^36 + 76*x^35 + 72*x^34 + 61*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 78*x^5 + 56*x^4 + 44*x^3 + 8*x^2 + 81*x + 40, x^41 + 76*x^39 + 112*x^38 + 46*x^37 + 64*x^36 + 12*x^35 + 112*x^34 + 29*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 46*x^5 + 64*x^4 + 108*x^3 + 112*x^2 + 49*x + 96, x^41 + 76*x^39 + 88*x^38 + 110*x^37 + 56*x^36 + 76*x^35 + 8*x^34 + 29*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 110*x^5 + 120*x^4 + 44*x^3 + 72*x^2 + 49*x + 40, x^41 + 76*x^39 + 24*x^38 + 110*x^37 + 120*x^36 + 12*x^35 + 8*x^34 + 93*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 110*x^5 + 56*x^4 + 108*x^3 + 72*x^2 + 113*x + 40, x^41 + 76*x^39 + 72*x^38 + 30*x^37 + 88*x^36 + 44*x^35 + 120*x^34 + 13*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 30*x^5 + 24*x^4 + 12*x^3 + 56*x^2 + 33*x + 40, x^41 + 76*x^39 + 80*x^38 + 62*x^37 + 80*x^36 + 108*x^35 + 112*x^34 + 45*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 62*x^5 + 80*x^4 + 76*x^3 + 112*x^2 + 65*x + 112, x^41 + 76*x^39 + 72*x^38 + 126*x^37 + 88*x^36 + 108*x^35 + 120*x^34 + 109*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 126*x^5 + 24*x^4 + 76*x^3 + 56*x^2 + x + 40, x^41 + 76*x^39 + 124*x^38 + 6*x^37 + 4*x^36 + 28*x^35 + 36*x^34 + 117*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 70*x^5 + 36*x^4 + 124*x^3 + 4*x^2 + 73*x + 124, x^41 + 76*x^39 + 62*x^37 + 44*x^35 + 64*x^34 + 109*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 62*x^5 + 12*x^3 + 64*x^2 + x + 64, x^41 + 76*x^39 + 56*x^38 + 46*x^37 + 24*x^36 + 12*x^35 + 104*x^34 + 29*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 46*x^5 + 88*x^4 + 108*x^3 + 40*x^2 + 49*x + 8, x^41 + 76*x^39 + 8*x^38 + 14*x^37 + 104*x^36 + 76*x^35 + 88*x^34 + 125*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 14*x^5 + 40*x^4 + 44*x^3 + 24*x^2 + 17*x + 120, x^41 + 76*x^39 + 100*x^38 + 22*x^37 + 12*x^36 + 124*x^35 + 92*x^34 + 5*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 86*x^5 + 108*x^4 + 92*x^3 + 124*x^2 + 89*x + 20, x^41 + 76*x^39 + 60*x^38 + 86*x^37 + 84*x^36 + 124*x^35 + 4*x^34 + 69*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 22*x^5 + 116*x^4 + 92*x^3 + 100*x^2 + 25*x + 12, x^41 + 76*x^39 + 52*x^38 + 118*x^37 + 60*x^36 + 60*x^35 + 12*x^34 + 101*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 54*x^5 + 28*x^4 + 28*x^3 + 44*x^2 + 57*x + 100, x^41 + 76*x^39 + 80*x^38 + 14*x^37 + 96*x^36 + 12*x^35 + 80*x^34 + 61*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 14*x^5 + 96*x^4 + 108*x^3 + 80*x^2 + 81*x, x^41 + 76*x^39 + 96*x^38 + 14*x^37 + 16*x^36 + 76*x^35 + 125*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 14*x^5 + 16*x^4 + 44*x^3 + 17*x + 16, x^41 + 76*x^39 + 116*x^38 + 6*x^37 + 76*x^36 + 28*x^35 + 108*x^34 + 117*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 70*x^5 + 44*x^4 + 124*x^3 + 12*x^2 + 73*x + 52, x^41 + 76*x^39 + 92*x^38 + 118*x^37 + 20*x^36 + 124*x^35 + 100*x^34 + 37*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 54*x^5 + 52*x^4 + 92*x^3 + 68*x^2 + 121*x + 76, x^41 + 76*x^39 + 56*x^38 + 94*x^37 + 40*x^36 + 108*x^35 + 72*x^34 + 13*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 94*x^5 + 104*x^4 + 76*x^3 + 8*x^2 + 33*x + 24, x^41 + 76*x^39 + 116*x^38 + 102*x^37 + 108*x^36 + 92*x^35 + 44*x^34 + 85*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 38*x^5 + 76*x^4 + 60*x^3 + 76*x^2 + 41*x + 84, x^41 + 76*x^39 + 124*x^38 + 86*x^37 + 20*x^36 + 60*x^35 + 4*x^34 + 5*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 22*x^5 + 52*x^4 + 28*x^3 + 100*x^2 + 89*x + 12, x^41 + 76*x^39 + 64*x^38 + 62*x^37 + 32*x^36 + 44*x^35 + 64*x^34 + 109*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 62*x^5 + 32*x^4 + 12*x^3 + 64*x^2 + x + 96, x^41 + 76*x^39 + 76*x^38 + 118*x^37 + 4*x^36 + 124*x^35 + 52*x^34 + 37*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 54*x^5 + 36*x^4 + 92*x^3 + 20*x^2 + 121*x + 28, x^41 + 76*x^39 + 8*x^38 + 110*x^37 + 72*x^36 + 12*x^35 + 24*x^34 + 93*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 110*x^5 + 8*x^4 + 108*x^3 + 88*x^2 + 113*x + 88, x^41 + 76*x^39 + 28*x^38 + 102*x^37 + 4*x^36 + 92*x^35 + 68*x^34 + 85*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 38*x^5 + 36*x^4 + 60*x^3 + 36*x^2 + 41*x + 60, x^41 + 76*x^39 + 4*x^38 + 102*x^37 + 124*x^36 + 92*x^35 + 92*x^34 + 85*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 38*x^5 + 92*x^4 + 60*x^3 + 124*x^2 + 41*x + 4, x^41 + 76*x^39 + 120*x^38 + 46*x^37 + 88*x^36 + 76*x^35 + 104*x^34 + 93*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 46*x^5 + 24*x^4 + 44*x^3 + 40*x^2 + 113*x + 8, x^41 + 76*x^39 + 110*x^37 + 48*x^36 + 12*x^35 + 96*x^34 + 93*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 110*x^5 + 48*x^4 + 108*x^3 + 96*x^2 + 113*x + 112, x^41 + 76*x^39 + 44*x^38 + 6*x^37 + 20*x^36 + 92*x^35 + 52*x^34 + 53*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 70*x^5 + 52*x^4 + 60*x^3 + 20*x^2 + 9*x + 44, x^41 + 76*x^39 + 60*x^38 + 22*x^37 + 84*x^36 + 124*x^35 + 4*x^34 + 5*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 86*x^5 + 116*x^4 + 92*x^3 + 100*x^2 + 89*x + 12, x^41 + 76*x^39 + 88*x^38 + 62*x^37 + 40*x^36 + 44*x^35 + 104*x^34 + 109*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 62*x^5 + 104*x^4 + 12*x^3 + 40*x^2 + x + 88, x^41 + 76*x^39 + 76*x^38 + 38*x^37 + 20*x^36 + 92*x^35 + 20*x^34 + 21*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 102*x^5 + 52*x^4 + 60*x^3 + 116*x^2 + 105*x + 44, x^41 + 76*x^39 + 4*x^38 + 118*x^37 + 76*x^36 + 124*x^35 + 60*x^34 + 37*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 54*x^5 + 44*x^4 + 92*x^3 + 92*x^2 + 121*x + 84, x^41 + 76*x^39 + 12*x^38 + 6*x^37 + 84*x^36 + 28*x^35 + 84*x^34 + 117*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 70*x^5 + 116*x^4 + 124*x^3 + 52*x^2 + 73*x + 108, x^41 + 76*x^39 + 84*x^38 + 38*x^37 + 108*x^36 + 28*x^35 + 76*x^34 + 85*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 102*x^5 + 76*x^4 + 124*x^3 + 108*x^2 + 41*x + 84, x^41 + 76*x^39 + 16*x^38 + 30*x^37 + 48*x^36 + 108*x^35 + 48*x^34 + 77*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 30*x^5 + 48*x^4 + 76*x^3 + 48*x^2 + 97*x + 16, x^41 + 76*x^39 + 8*x^38 + 62*x^37 + 56*x^36 + 44*x^35 + 56*x^34 + 109*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 62*x^5 + 120*x^4 + 12*x^3 + 120*x^2 + x + 72, x^41 + 76*x^39 + 124*x^38 + 118*x^37 + 52*x^36 + 60*x^35 + 4*x^34 + 101*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 54*x^5 + 84*x^4 + 28*x^3 + 100*x^2 + 57*x + 108, x^41 + 76*x^39 + 100*x^38 + 102*x^37 + 92*x^36 + 92*x^35 + 124*x^34 + 85*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 38*x^5 + 60*x^4 + 60*x^3 + 28*x^2 + 41*x + 36, x^41 + 76*x^39 + 124*x^38 + 70*x^37 + 4*x^36 + 28*x^35 + 36*x^34 + 53*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 6*x^5 + 36*x^4 + 124*x^3 + 4*x^2 + 9*x + 124, x^41 + 76*x^39 + 44*x^38 + 86*x^37 + 68*x^36 + 60*x^35 + 20*x^34 + 5*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 22*x^5 + 100*x^4 + 28*x^3 + 116*x^2 + 89*x + 28, x^41 + 76*x^39 + 80*x^38 + 62*x^37 + 80*x^36 + 44*x^35 + 48*x^34 + 109*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 62*x^5 + 80*x^4 + 12*x^3 + 48*x^2 + x + 48, x^41 + 76*x^39 + 100*x^38 + 54*x^37 + 108*x^36 + 124*x^35 + 92*x^34 + 101*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 118*x^5 + 76*x^4 + 92*x^3 + 124*x^2 + 57*x + 52, x^41 + 76*x^39 + 120*x^38 + 30*x^37 + 8*x^36 + 108*x^35 + 72*x^34 + 77*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 30*x^5 + 72*x^4 + 76*x^3 + 8*x^2 + 97*x + 120, x^41 + 76*x^39 + 112*x^38 + 110*x^37 + 76*x^35 + 48*x^34 + 29*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 110*x^5 + 44*x^3 + 48*x^2 + 49*x + 96, x^41 + 76*x^39 + 56*x^38 + 46*x^37 + 88*x^36 + 76*x^35 + 40*x^34 + 93*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 46*x^5 + 24*x^4 + 44*x^3 + 104*x^2 + 113*x + 8, x^41 + 76*x^39 + 88*x^38 + 78*x^37 + 88*x^36 + 76*x^35 + 8*x^34 + 61*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 78*x^5 + 24*x^4 + 44*x^3 + 72*x^2 + 81*x + 8, x^41 + 76*x^39 + 96*x^38 + 14*x^37 + 16*x^36 + 12*x^35 + 64*x^34 + 61*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 14*x^5 + 16*x^4 + 108*x^3 + 64*x^2 + 81*x + 80, x^41 + 76*x^39 + 40*x^38 + 110*x^37 + 8*x^36 + 12*x^35 + 56*x^34 + 93*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 110*x^5 + 72*x^4 + 108*x^3 + 120*x^2 + 113*x + 88, x^41 + 76*x^39 + 48*x^38 + 46*x^37 + 96*x^36 + 76*x^35 + 48*x^34 + 93*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 46*x^5 + 96*x^4 + 44*x^3 + 48*x^2 + 113*x + 64, x^41 + 76*x^39 + 40*x^38 + 78*x^37 + 40*x^36 + 12*x^35 + 56*x^34 + 125*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 78*x^5 + 104*x^4 + 108*x^3 + 120*x^2 + 17*x + 56, x^41 + 76*x^39 + 28*x^38 + 102*x^37 + 68*x^36 + 28*x^35 + 4*x^34 + 21*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 38*x^5 + 100*x^4 + 124*x^3 + 100*x^2 + 105*x + 60, x^41 + 76*x^39 + 80*x^38 + 78*x^37 + 32*x^36 + 76*x^35 + 16*x^34 + 61*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 78*x^5 + 32*x^4 + 44*x^3 + 16*x^2 + 81*x, x^41 + 76*x^39 + 76*x^38 + 118*x^37 + 68*x^36 + 124*x^35 + 52*x^34 + 37*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 54*x^5 + 100*x^4 + 92*x^3 + 20*x^2 + 121*x + 92, x^41 + 76*x^39 + 16*x^38 + 46*x^37 + 12*x^35 + 16*x^34 + 29*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 46*x^5 + 108*x^3 + 16*x^2 + 49*x + 96, x^41 + 76*x^39 + 116*x^38 + 70*x^37 + 76*x^36 + 28*x^35 + 108*x^34 + 53*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 6*x^5 + 44*x^4 + 124*x^3 + 12*x^2 + 9*x + 52, x^41 + 76*x^39 + 16*x^38 + 46*x^37 + 96*x^36 + 12*x^35 + 80*x^34 + 29*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 46*x^5 + 96*x^4 + 108*x^3 + 80*x^2 + 49*x + 64, x^41 + 76*x^39 + 76*x^38 + 102*x^37 + 84*x^36 + 92*x^35 + 20*x^34 + 85*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 38*x^5 + 116*x^4 + 60*x^3 + 116*x^2 + 41*x + 108, x^41 + 76*x^39 + 80*x^38 + 78*x^37 + 32*x^36 + 12*x^35 + 80*x^34 + 125*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 78*x^5 + 32*x^4 + 108*x^3 + 80*x^2 + 17*x + 64, x^41 + 76*x^39 + 44*x^38 + 54*x^37 + 4*x^36 + 60*x^35 + 84*x^34 + 37*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 118*x^5 + 36*x^4 + 28*x^3 + 52*x^2 + 121*x + 28, x^41 + 76*x^39 + 124*x^38 + 54*x^37 + 116*x^36 + 60*x^35 + 4*x^34 + 37*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 118*x^5 + 20*x^4 + 28*x^3 + 100*x^2 + 121*x + 44, x^41 + 76*x^39 + 4*x^38 + 22*x^37 + 44*x^36 + 60*x^35 + 124*x^34 + 69*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 86*x^5 + 12*x^4 + 28*x^3 + 28*x^2 + 25*x + 52, x^41 + 76*x^39 + 20*x^38 + 118*x^37 + 124*x^36 + 124*x^35 + 44*x^34 + 37*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 54*x^5 + 92*x^4 + 92*x^3 + 76*x^2 + 121*x + 36, x^41 + 76*x^39 + 100*x^38 + 86*x^37 + 12*x^36 + 60*x^35 + 28*x^34 + 5*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 22*x^5 + 108*x^4 + 28*x^3 + 60*x^2 + 89*x + 84, x^41 + 76*x^39 + 68*x^38 + 6*x^37 + 60*x^36 + 28*x^35 + 28*x^34 + 117*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 70*x^5 + 28*x^4 + 124*x^3 + 60*x^2 + 73*x + 68, x^41 + 76*x^39 + 104*x^38 + 126*x^37 + 24*x^36 + 108*x^35 + 24*x^34 + 109*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 126*x^5 + 88*x^4 + 76*x^3 + 88*x^2 + x + 40, x^41 + 76*x^39 + 40*x^38 + 14*x^37 + 104*x^36 + 76*x^35 + 120*x^34 + 125*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 14*x^5 + 40*x^4 + 44*x^3 + 56*x^2 + 17*x + 56, x^41 + 76*x^39 + 84*x^38 + 22*x^37 + 92*x^36 + 124*x^35 + 108*x^34 + 5*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 86*x^5 + 60*x^4 + 92*x^3 + 12*x^2 + 89*x + 68, x^41 + 76*x^39 + 110*x^37 + 112*x^36 + 12*x^35 + 96*x^34 + 93*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 110*x^5 + 112*x^4 + 108*x^3 + 96*x^2 + 113*x + 48, x^41 + 76*x^39 + 44*x^38 + 38*x^37 + 84*x^36 + 28*x^35 + 52*x^34 + 85*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 102*x^5 + 116*x^4 + 124*x^3 + 20*x^2 + 41*x + 108, x^41 + 76*x^39 + 72*x^38 + 30*x^37 + 24*x^36 + 108*x^35 + 56*x^34 + 77*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 30*x^5 + 88*x^4 + 76*x^3 + 120*x^2 + 97*x + 40, x^41 + 76*x^39 + 40*x^38 + 30*x^37 + 120*x^36 + 108*x^35 + 88*x^34 + 77*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 30*x^5 + 56*x^4 + 76*x^3 + 24*x^2 + 97*x + 72, x^41 + 76*x^39 + 40*x^38 + 94*x^37 + 24*x^36 + 108*x^35 + 24*x^34 + 13*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 94*x^5 + 88*x^4 + 76*x^3 + 88*x^2 + 33*x + 104, x^41 + 76*x^39 + 120*x^38 + 62*x^37 + 104*x^36 + 108*x^35 + 72*x^34 + 45*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 62*x^5 + 40*x^4 + 76*x^3 + 8*x^2 + 65*x + 24, x^41 + 76*x^39 + 88*x^38 + 78*x^37 + 120*x^36 + 12*x^35 + 8*x^34 + 125*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 78*x^5 + 56*x^4 + 108*x^3 + 72*x^2 + 17*x + 104, x^41 + 76*x^39 + 84*x^38 + 102*x^37 + 44*x^36 + 92*x^35 + 12*x^34 + 85*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 38*x^5 + 12*x^4 + 60*x^3 + 44*x^2 + 41*x + 84, x^41 + 76*x^39 + 96*x^38 + 30*x^37 + 96*x^36 + 44*x^35 + 32*x^34 + 13*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 30*x^5 + 96*x^4 + 12*x^3 + 32*x^2 + 33*x + 32, x^41 + 76*x^39 + 80*x^38 + 94*x^37 + 80*x^36 + 44*x^35 + 112*x^34 + 77*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 94*x^5 + 80*x^4 + 12*x^3 + 112*x^2 + 97*x + 112, x^41 + 76*x^39 + 96*x^38 + 94*x^37 + 64*x^36 + 44*x^35 + 96*x^34 + 77*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 94*x^5 + 64*x^4 + 12*x^3 + 96*x^2 + 97*x, x^41 + 76*x^39 + 52*x^38 + 6*x^37 + 76*x^36 + 92*x^35 + 108*x^34 + 53*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 70*x^5 + 44*x^4 + 60*x^3 + 12*x^2 + 9*x + 116, x^41 + 76*x^39 + 24*x^38 + 30*x^37 + 72*x^36 + 108*x^35 + 104*x^34 + 77*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 30*x^5 + 8*x^4 + 76*x^3 + 40*x^2 + 97*x + 120, x^41 + 76*x^39 + 16*x^38 + 126*x^37 + 80*x^36 + 44*x^35 + 112*x^34 + 45*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 126*x^5 + 80*x^4 + 12*x^3 + 112*x^2 + 65*x + 48, x^41 + 76*x^39 + 56*x^38 + 62*x^37 + 72*x^36 + 108*x^35 + 72*x^34 + 45*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 62*x^5 + 8*x^4 + 76*x^3 + 8*x^2 + 65*x + 120, x^41 + 76*x^39 + 68*x^38 + 86*x^37 + 12*x^36 + 124*x^35 + 60*x^34 + 69*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 22*x^5 + 108*x^4 + 92*x^3 + 92*x^2 + 25*x + 84, x^41 + 76*x^39 + 76*x^38 + 86*x^37 + 36*x^36 + 124*x^35 + 52*x^34 + 69*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 22*x^5 + 68*x^4 + 92*x^3 + 20*x^2 + 25*x + 124, x^41 + 76*x^39 + 8*x^38 + 94*x^37 + 24*x^36 + 108*x^35 + 120*x^34 + 13*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 94*x^5 + 88*x^4 + 76*x^3 + 56*x^2 + 33*x + 40, x^41 + 76*x^39 + 28*x^38 + 118*x^37 + 20*x^36 + 60*x^35 + 100*x^34 + 101*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 54*x^5 + 52*x^4 + 28*x^3 + 68*x^2 + 57*x + 12, x^41 + 76*x^39 + 124*x^38 + 118*x^37 + 116*x^36 + 124*x^35 + 68*x^34 + 37*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 54*x^5 + 20*x^4 + 92*x^3 + 36*x^2 + 121*x + 108, x^41 + 76*x^39 + 4*x^38 + 54*x^37 + 44*x^36 + 60*x^35 + 60*x^34 + 37*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 118*x^5 + 12*x^4 + 28*x^3 + 92*x^2 + 121*x + 116, x^41 + 76*x^39 + 4*x^38 + 38*x^37 + 60*x^36 + 92*x^35 + 92*x^34 + 21*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 102*x^5 + 28*x^4 + 60*x^3 + 124*x^2 + 105*x + 68, x^41 + 76*x^39 + 36*x^38 + 38*x^37 + 28*x^36 + 92*x^35 + 60*x^34 + 21*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 102*x^5 + 124*x^4 + 60*x^3 + 92*x^2 + 105*x + 100, x^41 + 76*x^39 + 36*x^38 + 6*x^37 + 28*x^36 + 28*x^35 + 60*x^34 + 117*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 70*x^5 + 124*x^4 + 124*x^3 + 92*x^2 + 73*x + 100, x^41 + 76*x^39 + 80*x^38 + 30*x^37 + 16*x^36 + 108*x^35 + 48*x^34 + 77*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 30*x^5 + 16*x^4 + 76*x^3 + 48*x^2 + 97*x + 112, x^41 + 76*x^39 + 76*x^38 + 70*x^37 + 84*x^36 + 92*x^35 + 84*x^34 + 117*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 6*x^5 + 116*x^4 + 60*x^3 + 52*x^2 + 73*x + 44, x^41 + 76*x^39 + 36*x^38 + 70*x^37 + 28*x^36 + 28*x^35 + 60*x^34 + 53*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 6*x^5 + 124*x^4 + 124*x^3 + 92*x^2 + 9*x + 100, x^41 + 76*x^39 + 116*x^38 + 22*x^37 + 92*x^36 + 60*x^35 + 76*x^34 + 69*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 86*x^5 + 60*x^4 + 28*x^3 + 108*x^2 + 25*x + 68, x^41 + 76*x^39 + 60*x^38 + 118*x^37 + 116*x^36 + 124*x^35 + 4*x^34 + 37*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 54*x^5 + 20*x^4 + 92*x^3 + 100*x^2 + 121*x + 108, x^41 + 76*x^39 + 84*x^38 + 22*x^37 + 28*x^36 + 124*x^35 + 108*x^34 + 5*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 86*x^5 + 124*x^4 + 92*x^3 + 12*x^2 + 89*x + 4, x^41 + 76*x^39 + 16*x^38 + 78*x^37 + 32*x^36 + 76*x^35 + 80*x^34 + 61*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 78*x^5 + 32*x^4 + 44*x^3 + 80*x^2 + 81*x, x^41 + 76*x^39 + 116*x^38 + 38*x^37 + 108*x^36 + 28*x^35 + 108*x^34 + 85*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 102*x^5 + 76*x^4 + 124*x^3 + 12*x^2 + 41*x + 20, x^41 + 76*x^39 + 92*x^38 + 22*x^37 + 116*x^36 + 124*x^35 + 100*x^34 + 5*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 86*x^5 + 20*x^4 + 92*x^3 + 68*x^2 + 89*x + 108, x^41 + 76*x^39 + 124*x^38 + 102*x^37 + 68*x^36 + 28*x^35 + 100*x^34 + 21*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 38*x^5 + 100*x^4 + 124*x^3 + 68*x^2 + 105*x + 124, x^41 + 76*x^39 + 124*x^38 + 22*x^37 + 84*x^36 + 60*x^35 + 4*x^34 + 69*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 86*x^5 + 116*x^4 + 28*x^3 + 100*x^2 + 25*x + 76, x^41 + 76*x^39 + 8*x^38 + 30*x^37 + 24*x^36 + 108*x^35 + 120*x^34 + 77*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 30*x^5 + 88*x^4 + 76*x^3 + 56*x^2 + 97*x + 40, x^41 + 76*x^39 + 80*x^38 + 14*x^37 + 12*x^35 + 16*x^34 + 61*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 14*x^5 + 108*x^3 + 16*x^2 + 81*x + 32, x^41 + 76*x^39 + 48*x^38 + 14*x^37 + 64*x^36 + 76*x^35 + 48*x^34 + 125*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 14*x^5 + 64*x^4 + 44*x^3 + 48*x^2 + 17*x + 96, x^41 + 76*x^39 + 68*x^38 + 86*x^37 + 76*x^36 + 124*x^35 + 60*x^34 + 69*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 22*x^5 + 44*x^4 + 92*x^3 + 92*x^2 + 25*x + 20, x^41 + 76*x^39 + 48*x^38 + 94*x^37 + 112*x^36 + 44*x^35 + 16*x^34 + 77*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 94*x^5 + 112*x^4 + 12*x^3 + 16*x^2 + 97*x + 80, x^41 + 76*x^39 + 20*x^38 + 6*x^37 + 44*x^36 + 28*x^35 + 76*x^34 + 117*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 70*x^5 + 12*x^4 + 124*x^3 + 108*x^2 + 73*x + 84, x^41 + 76*x^39 + 44*x^38 + 54*x^37 + 4*x^36 + 124*x^35 + 20*x^34 + 101*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 118*x^5 + 36*x^4 + 92*x^3 + 116*x^2 + 57*x + 92, x^41 + 76*x^39 + 68*x^38 + 38*x^37 + 28*x^36 + 92*x^35 + 92*x^34 + 21*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 102*x^5 + 124*x^4 + 60*x^3 + 124*x^2 + 105*x + 36, x^41 + 76*x^39 + 16*x^38 + 94*x^37 + 112*x^36 + 108*x^35 + 48*x^34 + 13*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 94*x^5 + 112*x^4 + 76*x^3 + 48*x^2 + 33*x + 80, x^41 + 76*x^39 + 24*x^38 + 126*x^37 + 104*x^36 + 108*x^35 + 104*x^34 + 109*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 126*x^5 + 40*x^4 + 76*x^3 + 40*x^2 + x + 88, x^41 + 76*x^39 + 4*x^38 + 86*x^37 + 44*x^36 + 124*x^35 + 60*x^34 + 69*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 22*x^5 + 12*x^4 + 92*x^3 + 92*x^2 + 25*x + 116, x^41 + 76*x^39 + 108*x^38 + 22*x^37 + 36*x^36 + 124*x^35 + 84*x^34 + 5*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 86*x^5 + 68*x^4 + 92*x^3 + 52*x^2 + 89*x + 60, x^41 + 76*x^39 + 92*x^38 + 102*x^37 + 4*x^36 + 92*x^35 + 4*x^34 + 85*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 38*x^5 + 36*x^4 + 60*x^3 + 100*x^2 + 41*x + 60, x^41 + 76*x^39 + 84*x^38 + 118*x^37 + 124*x^36 + 60*x^35 + 44*x^34 + 101*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 54*x^5 + 92*x^4 + 28*x^3 + 76*x^2 + 57*x + 100, x^41 + 76*x^39 + 72*x^38 + 14*x^37 + 72*x^36 + 12*x^35 + 24*x^34 + 61*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 14*x^5 + 8*x^4 + 108*x^3 + 88*x^2 + 81*x + 24, x^41 + 76*x^39 + 116*x^38 + 86*x^37 + 124*x^36 + 60*x^35 + 12*x^34 + 5*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 22*x^5 + 92*x^4 + 28*x^3 + 44*x^2 + 89*x + 100, x^41 + 76*x^39 + 48*x^38 + 14*x^37 + 76*x^35 + 48*x^34 + 125*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 14*x^5 + 44*x^3 + 48*x^2 + 17*x + 32, x^41 + 76*x^39 + 80*x^38 + 126*x^37 + 16*x^36 + 108*x^35 + 112*x^34 + 109*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 126*x^5 + 16*x^4 + 76*x^3 + 112*x^2 + x + 48, x^41 + 76*x^39 + 100*x^38 + 118*x^37 + 44*x^36 + 124*x^35 + 92*x^34 + 37*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 54*x^5 + 12*x^4 + 92*x^3 + 124*x^2 + 121*x + 116, x^41 + 76*x^39 + 68*x^38 + 38*x^37 + 60*x^36 + 92*x^35 + 28*x^34 + 21*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 102*x^5 + 28*x^4 + 60*x^3 + 60*x^2 + 105*x + 68, x^41 + 76*x^39 + 80*x^38 + 46*x^37 + 96*x^36 + 12*x^35 + 16*x^34 + 29*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 46*x^5 + 96*x^4 + 108*x^3 + 16*x^2 + 49*x + 64, x^41 + 76*x^39 + 76*x^38 + 70*x^37 + 52*x^36 + 28*x^35 + 84*x^34 + 53*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 6*x^5 + 84*x^4 + 124*x^3 + 52*x^2 + 9*x + 76, x^41 + 76*x^39 + 96*x^38 + 94*x^37 + 96*x^36 + 44*x^35 + 32*x^34 + 77*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 94*x^5 + 96*x^4 + 12*x^3 + 32*x^2 + 97*x + 32, x^41 + 76*x^39 + 96*x^38 + 110*x^37 + 16*x^36 + 12*x^35 + 93*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 110*x^5 + 16*x^4 + 108*x^3 + 113*x + 16, x^41 + 76*x^39 + 56*x^38 + 126*x^37 + 40*x^36 + 44*x^35 + 72*x^34 + 45*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 126*x^5 + 104*x^4 + 12*x^3 + 8*x^2 + 65*x + 24, x^41 + 76*x^39 + 88*x^38 + 46*x^37 + 24*x^36 + 76*x^35 + 72*x^34 + 93*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 46*x^5 + 88*x^4 + 44*x^3 + 8*x^2 + 113*x + 8, x^41 + 76*x^39 + 4*x^38 + 118*x^37 + 12*x^36 + 60*x^35 + 124*x^34 + 101*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 54*x^5 + 108*x^4 + 28*x^3 + 28*x^2 + 57*x + 84, x^41 + 76*x^39 + 124*x^38 + 22*x^37 + 116*x^36 + 60*x^35 + 68*x^34 + 69*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 86*x^5 + 20*x^4 + 28*x^3 + 36*x^2 + 25*x + 108, x^41 + 76*x^39 + 32*x^38 + 94*x^37 + 108*x^35 + 96*x^34 + 13*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 94*x^5 + 76*x^3 + 96*x^2 + 33*x, x^41 + 76*x^39 + 80*x^38 + 30*x^37 + 80*x^36 + 108*x^35 + 48*x^34 + 77*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 30*x^5 + 80*x^4 + 76*x^3 + 48*x^2 + 97*x + 48, x^41 + 76*x^39 + 12*x^38 + 54*x^37 + 4*x^36 + 124*x^35 + 116*x^34 + 101*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 118*x^5 + 36*x^4 + 92*x^3 + 84*x^2 + 57*x + 28, x^41 + 76*x^39 + 120*x^38 + 126*x^37 + 72*x^36 + 44*x^35 + 72*x^34 + 45*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 126*x^5 + 8*x^4 + 12*x^3 + 8*x^2 + 65*x + 56, x^41 + 76*x^39 + 64*x^38 + 126*x^37 + 32*x^36 + 44*x^35 + 64*x^34 + 45*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 126*x^5 + 32*x^4 + 12*x^3 + 64*x^2 + 65*x + 96, x^41 + 76*x^39 + 4*x^38 + 86*x^37 + 108*x^36 + 124*x^35 + 60*x^34 + 69*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 22*x^5 + 76*x^4 + 92*x^3 + 92*x^2 + 25*x + 52, x^41 + 76*x^39 + 124*x^38 + 102*x^37 + 36*x^36 + 28*x^35 + 36*x^34 + 21*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 38*x^5 + 68*x^4 + 124*x^3 + 4*x^2 + 105*x + 92, x^41 + 76*x^39 + 20*x^38 + 22*x^37 + 28*x^36 + 124*x^35 + 44*x^34 + 5*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 86*x^5 + 124*x^4 + 92*x^3 + 76*x^2 + 89*x + 4, x^41 + 76*x^39 + 60*x^38 + 102*x^37 + 4*x^36 + 28*x^35 + 36*x^34 + 21*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 38*x^5 + 36*x^4 + 124*x^3 + 4*x^2 + 105*x + 60, x^41 + 76*x^39 + 126*x^37 + 96*x^36 + 108*x^35 + 64*x^34 + 109*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 126*x^5 + 96*x^4 + 76*x^3 + 64*x^2 + x + 96, x^41 + 76*x^39 + 92*x^38 + 102*x^37 + 100*x^36 + 92*x^35 + 68*x^34 + 85*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 38*x^5 + 4*x^4 + 60*x^3 + 36*x^2 + 41*x + 28, x^41 + 76*x^39 + 76*x^38 + 70*x^37 + 84*x^36 + 28*x^35 + 20*x^34 + 53*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 6*x^5 + 116*x^4 + 124*x^3 + 116*x^2 + 9*x + 108, x^41 + 76*x^39 + 92*x^38 + 70*x^37 + 36*x^36 + 28*x^35 + 68*x^34 + 53*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 6*x^5 + 68*x^4 + 124*x^3 + 36*x^2 + 9*x + 92, x^41 + 76*x^39 + 68*x^38 + 118*x^37 + 76*x^36 + 124*x^35 + 124*x^34 + 37*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 54*x^5 + 44*x^4 + 92*x^3 + 28*x^2 + 121*x + 84, x^41 + 76*x^39 + 16*x^38 + 126*x^37 + 16*x^36 + 108*x^35 + 48*x^34 + 109*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 126*x^5 + 16*x^4 + 76*x^3 + 48*x^2 + x + 48, x^41 + 76*x^39 + 40*x^38 + 62*x^37 + 24*x^36 + 44*x^35 + 24*x^34 + 109*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 62*x^5 + 88*x^4 + 12*x^3 + 88*x^2 + x + 104, x^41 + 76*x^39 + 44*x^38 + 86*x^37 + 100*x^36 + 124*x^35 + 20*x^34 + 69*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 22*x^5 + 4*x^4 + 92*x^3 + 116*x^2 + 25*x + 124, x^41 + 76*x^39 + 76*x^38 + 22*x^37 + 68*x^36 + 124*x^35 + 116*x^34 + 5*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 86*x^5 + 100*x^4 + 92*x^3 + 84*x^2 + 89*x + 28, x^41 + 76*x^39 + 84*x^38 + 86*x^37 + 28*x^36 + 124*x^35 + 108*x^34 + 69*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 22*x^5 + 124*x^4 + 92*x^3 + 12*x^2 + 25*x + 4, x^41 + 76*x^39 + 76*x^38 + 118*x^37 + 100*x^36 + 124*x^35 + 116*x^34 + 37*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 54*x^5 + 4*x^4 + 92*x^3 + 84*x^2 + 121*x + 124, x^41 + 76*x^39 + 120*x^38 + 46*x^37 + 56*x^36 + 76*x^35 + 40*x^34 + 93*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 46*x^5 + 120*x^4 + 44*x^3 + 104*x^2 + 113*x + 104, x^41 + 76*x^39 + 32*x^38 + 62*x^37 + 64*x^36 + 44*x^35 + 96*x^34 + 109*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 62*x^5 + 64*x^4 + 12*x^3 + 96*x^2 + x + 64, x^41 + 76*x^39 + 94*x^37 + 108*x^35 + 64*x^34 + 13*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 94*x^5 + 76*x^3 + 64*x^2 + 33*x + 64, x^41 + 76*x^39 + 36*x^38 + 118*x^37 + 12*x^36 + 124*x^35 + 92*x^34 + 37*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 54*x^5 + 108*x^4 + 92*x^3 + 124*x^2 + 121*x + 84, x^41 + 76*x^39 + 60*x^38 + 6*x^37 + 100*x^36 + 28*x^35 + 36*x^34 + 117*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 70*x^5 + 4*x^4 + 124*x^3 + 4*x^2 + 73*x + 92, x^41 + 76*x^39 + 104*x^38 + 110*x^37 + 104*x^36 + 12*x^35 + 56*x^34 + 93*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 110*x^5 + 40*x^4 + 108*x^3 + 120*x^2 + 113*x + 56, x^41 + 76*x^39 + 60*x^38 + 70*x^37 + 100*x^36 + 28*x^35 + 36*x^34 + 53*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 6*x^5 + 4*x^4 + 124*x^3 + 4*x^2 + 9*x + 92, x^41 + 76*x^39 + 4*x^38 + 38*x^37 + 60*x^36 + 28*x^35 + 28*x^34 + 85*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 102*x^5 + 28*x^4 + 124*x^3 + 60*x^2 + 41*x + 4, x^41 + 76*x^39 + 8*x^38 + 94*x^37 + 88*x^36 + 108*x^35 + 120*x^34 + 13*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 94*x^5 + 24*x^4 + 76*x^3 + 56*x^2 + 33*x + 104, x^41 + 76*x^39 + 4*x^38 + 6*x^37 + 124*x^36 + 92*x^35 + 28*x^34 + 53*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 70*x^5 + 92*x^4 + 60*x^3 + 60*x^2 + 9*x + 68, x^41 + 76*x^39 + 40*x^38 + 30*x^37 + 56*x^36 + 108*x^35 + 88*x^34 + 77*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 30*x^5 + 120*x^4 + 76*x^3 + 24*x^2 + 97*x + 8, x^41 + 76*x^39 + 28*x^38 + 22*x^37 + 84*x^36 + 60*x^35 + 36*x^34 + 69*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 86*x^5 + 116*x^4 + 28*x^3 + 4*x^2 + 25*x + 12, x^41 + 76*x^39 + 12*x^38 + 54*x^37 + 68*x^36 + 124*x^35 + 116*x^34 + 101*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 118*x^5 + 100*x^4 + 92*x^3 + 84*x^2 + 57*x + 92, x^41 + 76*x^39 + 124*x^38 + 86*x^37 + 52*x^36 + 60*x^35 + 68*x^34 + 5*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 22*x^5 + 84*x^4 + 28*x^3 + 36*x^2 + 89*x + 44, x^41 + 76*x^39 + 48*x^38 + 110*x^37 + 32*x^36 + 76*x^35 + 48*x^34 + 29*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 110*x^5 + 32*x^4 + 44*x^3 + 48*x^2 + 49*x, x^41 + 76*x^39 + 32*x^38 + 14*x^37 + 80*x^36 + 12*x^35 + 61*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 14*x^5 + 80*x^4 + 108*x^3 + 81*x + 16, x^41 + 76*x^39 + 76*x^38 + 54*x^37 + 36*x^36 + 60*x^35 + 52*x^34 + 37*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 118*x^5 + 68*x^4 + 28*x^3 + 20*x^2 + 121*x + 124, x^41 + 76*x^39 + 20*x^38 + 38*x^37 + 76*x^36 + 28*x^35 + 76*x^34 + 85*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 102*x^5 + 44*x^4 + 124*x^3 + 108*x^2 + 41*x + 52, x^41 + 76*x^39 + 76*x^38 + 70*x^37 + 116*x^36 + 28*x^35 + 84*x^34 + 53*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 6*x^5 + 20*x^4 + 124*x^3 + 52*x^2 + 9*x + 12, x^41 + 76*x^39 + 28*x^38 + 38*x^37 + 4*x^36 + 28*x^35 + 4*x^34 + 85*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 102*x^5 + 36*x^4 + 124*x^3 + 100*x^2 + 41*x + 124, x^41 + 76*x^39 + 12*x^38 + 102*x^37 + 116*x^36 + 92*x^35 + 20*x^34 + 85*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 38*x^5 + 20*x^4 + 60*x^3 + 116*x^2 + 41*x + 12, x^41 + 76*x^39 + 84*x^38 + 54*x^37 + 124*x^36 + 124*x^35 + 108*x^34 + 101*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 118*x^5 + 92*x^4 + 92*x^3 + 12*x^2 + 57*x + 36, x^41 + 76*x^39 + 104*x^38 + 78*x^37 + 72*x^36 + 12*x^35 + 56*x^34 + 125*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 78*x^5 + 8*x^4 + 108*x^3 + 120*x^2 + 17*x + 88, x^41 + 76*x^39 + 124*x^38 + 102*x^37 + 68*x^36 + 92*x^35 + 36*x^34 + 85*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 38*x^5 + 100*x^4 + 60*x^3 + 4*x^2 + 41*x + 60, x^41 + 76*x^39 + 40*x^38 + 14*x^37 + 72*x^36 + 76*x^35 + 56*x^34 + 125*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 14*x^5 + 8*x^4 + 44*x^3 + 120*x^2 + 17*x + 24, x^41 + 76*x^39 + 40*x^38 + 126*x^37 + 56*x^36 + 108*x^35 + 24*x^34 + 109*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 126*x^5 + 120*x^4 + 76*x^3 + 88*x^2 + x + 72, x^41 + 76*x^39 + 116*x^38 + 118*x^37 + 28*x^36 + 60*x^35 + 12*x^34 + 101*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 54*x^5 + 124*x^4 + 28*x^3 + 44*x^2 + 57*x + 68, x^41 + 76*x^39 + 48*x^38 + 14*x^37 + 96*x^36 + 76*x^35 + 112*x^34 + 125*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 14*x^5 + 96*x^4 + 44*x^3 + 112*x^2 + 17*x, x^41 + 76*x^39 + 30*x^37 + 96*x^36 + 108*x^35 + 77*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 30*x^5 + 96*x^4 + 76*x^3 + 97*x + 32, x^41 + 76*x^39 + 72*x^38 + 62*x^37 + 120*x^36 + 108*x^35 + 56*x^34 + 45*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 62*x^5 + 56*x^4 + 76*x^3 + 120*x^2 + 65*x + 72, x^41 + 76*x^39 + 116*x^38 + 38*x^37 + 108*x^36 + 92*x^35 + 44*x^34 + 21*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 102*x^5 + 76*x^4 + 60*x^3 + 76*x^2 + 105*x + 84, x^41 + 76*x^39 + 36*x^38 + 38*x^37 + 124*x^36 + 28*x^35 + 60*x^34 + 85*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 102*x^5 + 92*x^4 + 124*x^3 + 92*x^2 + 41*x + 4, x^41 + 76*x^39 + 20*x^38 + 22*x^37 + 28*x^36 + 60*x^35 + 108*x^34 + 69*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 86*x^5 + 124*x^4 + 28*x^3 + 12*x^2 + 25*x + 68, x^41 + 76*x^39 + 80*x^38 + 110*x^37 + 64*x^36 + 12*x^35 + 80*x^34 + 93*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 110*x^5 + 64*x^4 + 108*x^3 + 80*x^2 + 113*x + 32, x^41 + 76*x^39 + 116*x^38 + 6*x^37 + 108*x^36 + 28*x^35 + 44*x^34 + 117*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 70*x^5 + 76*x^4 + 124*x^3 + 76*x^2 + 73*x + 84, x^41 + 76*x^39 + 112*x^38 + 62*x^37 + 112*x^36 + 44*x^35 + 16*x^34 + 109*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 62*x^5 + 112*x^4 + 12*x^3 + 16*x^2 + x + 16, x^41 + 76*x^39 + 28*x^38 + 38*x^37 + 4*x^36 + 92*x^35 + 68*x^34 + 21*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 102*x^5 + 36*x^4 + 60*x^3 + 36*x^2 + 105*x + 60, x^41 + 76*x^39 + 76*x^38 + 22*x^37 + 100*x^36 + 124*x^35 + 52*x^34 + 5*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 86*x^5 + 4*x^4 + 92*x^3 + 20*x^2 + 89*x + 60, x^41 + 76*x^39 + 108*x^38 + 118*x^37 + 68*x^36 + 124*x^35 + 84*x^34 + 37*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 54*x^5 + 100*x^4 + 92*x^3 + 52*x^2 + 121*x + 28, x^41 + 76*x^39 + 68*x^38 + 54*x^37 + 76*x^36 + 60*x^35 + 60*x^34 + 37*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 118*x^5 + 44*x^4 + 28*x^3 + 92*x^2 + 121*x + 20, x^41 + 76*x^39 + 16*x^38 + 30*x^37 + 112*x^36 + 108*x^35 + 48*x^34 + 77*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 30*x^5 + 112*x^4 + 76*x^3 + 48*x^2 + 97*x + 80, x^41 + 76*x^39 + 88*x^38 + 78*x^37 + 24*x^36 + 12*x^35 + 72*x^34 + 125*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 78*x^5 + 88*x^4 + 108*x^3 + 8*x^2 + 17*x + 8, x^41 + 76*x^39 + 24*x^38 + 46*x^37 + 24*x^36 + 76*x^35 + 8*x^34 + 93*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 46*x^5 + 88*x^4 + 44*x^3 + 72*x^2 + 113*x + 8, x^41 + 76*x^39 + 104*x^38 + 78*x^37 + 40*x^36 + 12*x^35 + 120*x^34 + 125*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 78*x^5 + 104*x^4 + 108*x^3 + 56*x^2 + 17*x + 56, x^41 + 76*x^39 + 4*x^38 + 118*x^37 + 44*x^36 + 60*x^35 + 60*x^34 + 101*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 54*x^5 + 12*x^4 + 28*x^3 + 92*x^2 + 57*x + 116, x^41 + 76*x^39 + 68*x^38 + 86*x^37 + 12*x^36 + 60*x^35 + 124*x^34 + 5*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 22*x^5 + 108*x^4 + 28*x^3 + 28*x^2 + 89*x + 20, x^41 + 76*x^39 + 92*x^38 + 6*x^37 + 36*x^36 + 92*x^35 + 4*x^34 + 53*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 70*x^5 + 68*x^4 + 60*x^3 + 100*x^2 + 9*x + 28, x^41 + 76*x^39 + 84*x^38 + 102*x^37 + 108*x^36 + 28*x^35 + 76*x^34 + 21*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 38*x^5 + 76*x^4 + 124*x^3 + 108*x^2 + 105*x + 84, x^41 + 76*x^39 + 60*x^38 + 54*x^37 + 84*x^36 + 60*x^35 + 4*x^34 + 37*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 118*x^5 + 116*x^4 + 28*x^3 + 100*x^2 + 121*x + 12, x^41 + 76*x^39 + 124*x^38 + 102*x^37 + 36*x^36 + 92*x^35 + 100*x^34 + 85*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 38*x^5 + 68*x^4 + 60*x^3 + 68*x^2 + 41*x + 28, x^41 + 76*x^39 + 14*x^37 + 112*x^36 + 12*x^35 + 32*x^34 + 61*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 14*x^5 + 112*x^4 + 108*x^3 + 32*x^2 + 81*x + 112, x^41 + 76*x^39 + 100*x^38 + 38*x^37 + 92*x^36 + 92*x^35 + 124*x^34 + 21*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 102*x^5 + 60*x^4 + 60*x^3 + 28*x^2 + 105*x + 36, x^41 + 76*x^39 + 12*x^38 + 118*x^37 + 36*x^36 + 60*x^35 + 116*x^34 + 101*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 54*x^5 + 68*x^4 + 28*x^3 + 84*x^2 + 57*x + 124, x^41 + 76*x^39 + 96*x^38 + 14*x^37 + 80*x^36 + 76*x^35 + 125*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 14*x^5 + 80*x^4 + 44*x^3 + 17*x + 80, x^41 + 76*x^39 + 32*x^38 + 94*x^37 + 96*x^36 + 108*x^35 + 32*x^34 + 13*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 94*x^5 + 96*x^4 + 76*x^3 + 32*x^2 + 33*x + 96, x^41 + 76*x^39 + 68*x^38 + 54*x^37 + 44*x^36 + 60*x^35 + 124*x^34 + 37*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 118*x^5 + 12*x^4 + 28*x^3 + 28*x^2 + 121*x + 116, x^41 + 76*x^39 + 16*x^38 + 62*x^37 + 80*x^36 + 44*x^35 + 112*x^34 + 109*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 62*x^5 + 80*x^4 + 12*x^3 + 112*x^2 + x + 48, x^41 + 76*x^39 + 108*x^38 + 38*x^37 + 20*x^36 + 92*x^35 + 52*x^34 + 21*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 102*x^5 + 52*x^4 + 60*x^3 + 20*x^2 + 105*x + 108, x^41 + 76*x^39 + 36*x^38 + 102*x^37 + 124*x^36 + 92*x^35 + 124*x^34 + 85*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 38*x^5 + 92*x^4 + 60*x^3 + 28*x^2 + 41*x + 68, x^41 + 76*x^39 + 32*x^38 + 62*x^37 + 96*x^36 + 108*x^35 + 96*x^34 + 45*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 62*x^5 + 96*x^4 + 76*x^3 + 96*x^2 + 65*x + 32, x^41 + 76*x^39 + 60*x^38 + 118*x^37 + 52*x^36 + 60*x^35 + 68*x^34 + 101*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 54*x^5 + 84*x^4 + 28*x^3 + 36*x^2 + 57*x + 108, x^41 + 76*x^39 + 96*x^38 + 126*x^37 + 32*x^36 + 44*x^35 + 96*x^34 + 45*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 126*x^5 + 32*x^4 + 12*x^3 + 96*x^2 + 65*x + 32, x^41 + 76*x^39 + 64*x^38 + 62*x^37 + 108*x^35 + 64*x^34 + 45*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 62*x^5 + 76*x^3 + 64*x^2 + 65*x, x^41 + 76*x^39 + 36*x^38 + 54*x^37 + 108*x^36 + 124*x^35 + 28*x^34 + 101*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 118*x^5 + 76*x^4 + 92*x^3 + 60*x^2 + 57*x + 52, x^41 + 76*x^39 + 68*x^38 + 70*x^37 + 92*x^36 + 28*x^35 + 92*x^34 + 53*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 6*x^5 + 60*x^4 + 124*x^3 + 124*x^2 + 9*x + 100, x^41 + 76*x^39 + 52*x^38 + 22*x^37 + 28*x^36 + 60*x^35 + 12*x^34 + 69*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 86*x^5 + 124*x^4 + 28*x^3 + 44*x^2 + 25*x + 4, x^41 + 76*x^39 + 120*x^38 + 62*x^37 + 40*x^36 + 108*x^35 + 72*x^34 + 45*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 62*x^5 + 104*x^4 + 76*x^3 + 8*x^2 + 65*x + 88, x^41 + 76*x^39 + 68*x^38 + 70*x^37 + 124*x^36 + 28*x^35 + 28*x^34 + 53*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 6*x^5 + 92*x^4 + 124*x^3 + 60*x^2 + 9*x + 4, x^41 + 76*x^39 + 104*x^38 + 46*x^37 + 40*x^36 + 12*x^35 + 56*x^34 + 29*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 46*x^5 + 104*x^4 + 108*x^3 + 120*x^2 + 49*x + 120, x^41 + 76*x^39 + 96*x^38 + 126*x^37 + 96*x^36 + 44*x^35 + 96*x^34 + 45*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 126*x^5 + 96*x^4 + 12*x^3 + 96*x^2 + 65*x + 96, x^41 + 76*x^39 + 76*x^38 + 70*x^37 + 20*x^36 + 92*x^35 + 84*x^34 + 117*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 6*x^5 + 52*x^4 + 60*x^3 + 52*x^2 + 73*x + 108, x^41 + 76*x^39 + 108*x^38 + 118*x^37 + 36*x^36 + 124*x^35 + 20*x^34 + 37*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 54*x^5 + 68*x^4 + 92*x^3 + 116*x^2 + 121*x + 124, x^41 + 76*x^39 + 48*x^38 + 110*x^37 + 64*x^36 + 12*x^35 + 48*x^34 + 93*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 110*x^5 + 64*x^4 + 108*x^3 + 48*x^2 + 113*x + 96, x^41 + 76*x^39 + 56*x^38 + 46*x^37 + 120*x^36 + 76*x^35 + 104*x^34 + 93*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 46*x^5 + 56*x^4 + 44*x^3 + 40*x^2 + 113*x + 40, x^41 + 76*x^39 + 44*x^38 + 118*x^37 + 68*x^36 + 60*x^35 + 84*x^34 + 101*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 54*x^5 + 100*x^4 + 28*x^3 + 52*x^2 + 57*x + 92, x^41 + 76*x^39 + 108*x^38 + 118*x^37 + 4*x^36 + 124*x^35 + 84*x^34 + 37*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 54*x^5 + 36*x^4 + 92*x^3 + 52*x^2 + 121*x + 92, x^41 + 76*x^39 + 100*x^38 + 86*x^37 + 108*x^36 + 124*x^35 + 28*x^34 + 69*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 22*x^5 + 76*x^4 + 92*x^3 + 60*x^2 + 25*x + 116, x^41 + 76*x^39 + 24*x^38 + 126*x^37 + 40*x^36 + 108*x^35 + 104*x^34 + 109*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 126*x^5 + 104*x^4 + 76*x^3 + 40*x^2 + x + 24, x^41 + 76*x^39 + 76*x^38 + 118*x^37 + 36*x^36 + 124*x^35 + 116*x^34 + 37*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 54*x^5 + 68*x^4 + 92*x^3 + 84*x^2 + 121*x + 60, x^41 + 76*x^39 + 80*x^38 + 14*x^37 + 64*x^36 + 76*x^35 + 80*x^34 + 125*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 14*x^5 + 64*x^4 + 44*x^3 + 80*x^2 + 17*x + 32, x^41 + 76*x^39 + 44*x^38 + 54*x^37 + 100*x^36 + 60*x^35 + 20*x^34 + 37*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 118*x^5 + 4*x^4 + 28*x^3 + 116*x^2 + 121*x + 124, x^41 + 76*x^39 + 52*x^38 + 118*x^37 + 124*x^36 + 60*x^35 + 12*x^34 + 101*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 54*x^5 + 92*x^4 + 28*x^3 + 44*x^2 + 57*x + 36, x^41 + 76*x^39 + 56*x^38 + 78*x^37 + 56*x^36 + 12*x^35 + 104*x^34 + 125*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 78*x^5 + 120*x^4 + 108*x^3 + 40*x^2 + 17*x + 104, x^41 + 76*x^39 + 62*x^37 + 32*x^36 + 108*x^35 + 64*x^34 + 45*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 62*x^5 + 32*x^4 + 76*x^3 + 64*x^2 + 65*x + 32, x^41 + 76*x^39 + 84*x^38 + 38*x^37 + 44*x^36 + 92*x^35 + 12*x^34 + 21*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 102*x^5 + 12*x^4 + 60*x^3 + 44*x^2 + 105*x + 84, x^41 + 76*x^39 + 124*x^38 + 118*x^37 + 84*x^36 + 124*x^35 + 4*x^34 + 37*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 54*x^5 + 116*x^4 + 92*x^3 + 100*x^2 + 121*x + 76, x^41 + 76*x^39 + 44*x^38 + 6*x^37 + 20*x^36 + 28*x^35 + 116*x^34 + 117*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 70*x^5 + 52*x^4 + 124*x^3 + 84*x^2 + 73*x + 108, x^41 + 76*x^39 + 44*x^38 + 70*x^37 + 20*x^36 + 28*x^35 + 116*x^34 + 53*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 6*x^5 + 52*x^4 + 124*x^3 + 84*x^2 + 9*x + 108, x^41 + 76*x^39 + 8*x^38 + 126*x^37 + 24*x^36 + 108*x^35 + 56*x^34 + 109*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 126*x^5 + 88*x^4 + 76*x^3 + 120*x^2 + x + 104, x^41 + 76*x^39 + 16*x^38 + 62*x^37 + 48*x^36 + 44*x^35 + 48*x^34 + 109*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 62*x^5 + 48*x^4 + 12*x^3 + 48*x^2 + x + 16, x^41 + 76*x^39 + 36*x^38 + 118*x^37 + 108*x^36 + 124*x^35 + 28*x^34 + 37*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 54*x^5 + 76*x^4 + 92*x^3 + 60*x^2 + 121*x + 52, x^41 + 76*x^39 + 108*x^38 + 70*x^37 + 52*x^36 + 92*x^35 + 52*x^34 + 117*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 6*x^5 + 84*x^4 + 60*x^3 + 20*x^2 + 73*x + 76, x^41 + 76*x^39 + 80*x^38 + 46*x^37 + 76*x^35 + 16*x^34 + 93*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 46*x^5 + 44*x^3 + 16*x^2 + 113*x + 32, x^41 + 76*x^39 + 124*x^38 + 6*x^37 + 36*x^36 + 28*x^35 + 100*x^34 + 117*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 70*x^5 + 68*x^4 + 124*x^3 + 68*x^2 + 73*x + 28, x^41 + 76*x^39 + 64*x^38 + 30*x^37 + 44*x^35 + 64*x^34 + 13*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 30*x^5 + 12*x^3 + 64*x^2 + 33*x, x^41 + 76*x^39 + 40*x^38 + 94*x^37 + 120*x^36 + 44*x^35 + 24*x^34 + 77*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 94*x^5 + 56*x^4 + 12*x^3 + 88*x^2 + 97*x + 8, x^41 + 76*x^39 + 20*x^38 + 22*x^37 + 92*x^36 + 60*x^35 + 108*x^34 + 69*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 86*x^5 + 60*x^4 + 28*x^3 + 12*x^2 + 25*x + 4, x^41 + 76*x^39 + 104*x^38 + 78*x^37 + 104*x^36 + 76*x^35 + 56*x^34 + 61*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 78*x^5 + 40*x^4 + 44*x^3 + 120*x^2 + 81*x + 56, x^41 + 76*x^39 + 20*x^38 + 54*x^37 + 92*x^36 + 60*x^35 + 44*x^34 + 37*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 118*x^5 + 60*x^4 + 28*x^3 + 76*x^2 + 121*x + 68, x^41 + 76*x^39 + 120*x^38 + 62*x^37 + 8*x^36 + 108*x^35 + 8*x^34 + 45*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 62*x^5 + 72*x^4 + 76*x^3 + 72*x^2 + 65*x + 56, x^41 + 76*x^39 + 48*x^38 + 30*x^37 + 16*x^36 + 108*x^35 + 16*x^34 + 77*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 30*x^5 + 16*x^4 + 76*x^3 + 16*x^2 + 97*x + 48, x^41 + 76*x^39 + 44*x^38 + 102*x^37 + 20*x^36 + 28*x^35 + 52*x^34 + 21*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 38*x^5 + 52*x^4 + 124*x^3 + 20*x^2 + 105*x + 44, x^41 + 76*x^39 + 124*x^38 + 38*x^37 + 4*x^36 + 92*x^35 + 36*x^34 + 21*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 102*x^5 + 36*x^4 + 60*x^3 + 4*x^2 + 105*x + 124, x^41 + 76*x^39 + 76*x^38 + 54*x^37 + 100*x^36 + 60*x^35 + 52*x^34 + 37*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 118*x^5 + 4*x^4 + 28*x^3 + 20*x^2 + 121*x + 60, x^41 + 76*x^39 + 8*x^38 + 30*x^37 + 56*x^36 + 44*x^35 + 120*x^34 + 13*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 30*x^5 + 120*x^4 + 12*x^3 + 56*x^2 + 33*x + 8, x^41 + 76*x^39 + 4*x^38 + 22*x^37 + 12*x^36 + 124*x^35 + 124*x^34 + 5*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 86*x^5 + 108*x^4 + 92*x^3 + 28*x^2 + 89*x + 84, x^41 + 76*x^39 + 12*x^38 + 86*x^37 + 100*x^36 + 60*x^35 + 52*x^34 + 5*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 22*x^5 + 4*x^4 + 28*x^3 + 20*x^2 + 89*x + 124, x^41 + 76*x^39 + 16*x^38 + 94*x^37 + 48*x^36 + 44*x^35 + 112*x^34 + 77*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 94*x^5 + 48*x^4 + 12*x^3 + 112*x^2 + 97*x + 80, x^41 + 76*x^39 + 108*x^38 + 38*x^37 + 20*x^36 + 28*x^35 + 116*x^34 + 85*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 102*x^5 + 52*x^4 + 124*x^3 + 84*x^2 + 41*x + 44, x^41 + 76*x^39 + 60*x^38 + 70*x^37 + 68*x^36 + 92*x^35 + 36*x^34 + 117*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 6*x^5 + 100*x^4 + 60*x^3 + 4*x^2 + 73*x + 124, x^41 + 76*x^39 + 48*x^38 + 30*x^37 + 112*x^36 + 108*x^35 + 80*x^34 + 77*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 30*x^5 + 112*x^4 + 76*x^3 + 80*x^2 + 97*x + 16, x^41 + 76*x^39 + 60*x^38 + 6*x^37 + 68*x^36 + 92*x^35 + 36*x^34 + 53*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 70*x^5 + 100*x^4 + 60*x^3 + 4*x^2 + 9*x + 124, x^41 + 76*x^39 + 32*x^38 + 126*x^37 + 64*x^36 + 44*x^35 + 96*x^34 + 45*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 126*x^5 + 64*x^4 + 12*x^3 + 96*x^2 + 65*x + 64, x^41 + 76*x^39 + 28*x^38 + 54*x^37 + 20*x^36 + 60*x^35 + 100*x^34 + 37*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 118*x^5 + 52*x^4 + 28*x^3 + 68*x^2 + 121*x + 12, x^41 + 76*x^39 + 92*x^38 + 54*x^37 + 52*x^36 + 124*x^35 + 36*x^34 + 101*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 118*x^5 + 84*x^4 + 92*x^3 + 4*x^2 + 57*x + 108, x^41 + 76*x^39 + 120*x^38 + 46*x^37 + 24*x^36 + 76*x^35 + 104*x^34 + 93*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 46*x^5 + 88*x^4 + 44*x^3 + 40*x^2 + 113*x + 72, x^41 + 76*x^39 + 120*x^38 + 126*x^37 + 104*x^36 + 44*x^35 + 8*x^34 + 45*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 126*x^5 + 40*x^4 + 12*x^3 + 72*x^2 + 65*x + 88, x^41 + 76*x^39 + 88*x^38 + 30*x^37 + 104*x^36 + 108*x^35 + 104*x^34 + 77*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 30*x^5 + 40*x^4 + 76*x^3 + 40*x^2 + 97*x + 24, x^41 + 76*x^39 + 40*x^38 + 30*x^37 + 120*x^36 + 44*x^35 + 24*x^34 + 13*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 30*x^5 + 56*x^4 + 12*x^3 + 88*x^2 + 33*x + 8, x^41 + 76*x^39 + 8*x^38 + 62*x^37 + 56*x^36 + 108*x^35 + 120*x^34 + 45*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 62*x^5 + 120*x^4 + 76*x^3 + 56*x^2 + 65*x + 8, x^41 + 76*x^39 + 96*x^38 + 46*x^37 + 80*x^36 + 76*x^35 + 64*x^34 + 93*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 46*x^5 + 80*x^4 + 44*x^3 + 64*x^2 + 113*x + 16, x^41 + 76*x^39 + 120*x^38 + 78*x^37 + 24*x^36 + 12*x^35 + 104*x^34 + 125*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 78*x^5 + 88*x^4 + 108*x^3 + 40*x^2 + 17*x + 72, x^41 + 76*x^39 + 84*x^38 + 38*x^37 + 76*x^36 + 28*x^35 + 12*x^34 + 85*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 102*x^5 + 44*x^4 + 124*x^3 + 44*x^2 + 41*x + 52, x^41 + 76*x^39 + 84*x^38 + 70*x^37 + 12*x^36 + 92*x^35 + 12*x^34 + 117*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 6*x^5 + 108*x^4 + 60*x^3 + 44*x^2 + 73*x + 116, x^41 + 76*x^39 + 112*x^38 + 62*x^37 + 112*x^36 + 108*x^35 + 80*x^34 + 45*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 62*x^5 + 112*x^4 + 76*x^3 + 80*x^2 + 65*x + 80, x^41 + 76*x^39 + 84*x^38 + 6*x^37 + 12*x^36 + 92*x^35 + 12*x^34 + 53*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 70*x^5 + 108*x^4 + 60*x^3 + 44*x^2 + 9*x + 116, x^41 + 76*x^39 + 60*x^38 + 22*x^37 + 84*x^36 + 60*x^35 + 68*x^34 + 69*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 86*x^5 + 116*x^4 + 28*x^3 + 36*x^2 + 25*x + 76, x^41 + 76*x^39 + 112*x^38 + 14*x^37 + 76*x^35 + 112*x^34 + 125*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 14*x^5 + 44*x^3 + 112*x^2 + 17*x + 32, x^41 + 76*x^39 + 20*x^38 + 70*x^37 + 76*x^36 + 92*x^35 + 76*x^34 + 117*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 6*x^5 + 44*x^4 + 60*x^3 + 108*x^2 + 73*x + 52, x^41 + 76*x^39 + 84*x^38 + 38*x^37 + 76*x^36 + 92*x^35 + 76*x^34 + 21*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 102*x^5 + 44*x^4 + 60*x^3 + 108*x^2 + 105*x + 116, x^41 + 76*x^39 + 48*x^38 + 62*x^37 + 80*x^36 + 44*x^35 + 16*x^34 + 109*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 62*x^5 + 80*x^4 + 12*x^3 + 16*x^2 + x + 112, x^41 + 76*x^39 + 76*x^38 + 102*x^37 + 20*x^36 + 28*x^35 + 84*x^34 + 21*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 38*x^5 + 52*x^4 + 124*x^3 + 52*x^2 + 105*x + 108, x^41 + 76*x^39 + 124*x^38 + 70*x^37 + 36*x^36 + 28*x^35 + 100*x^34 + 53*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 6*x^5 + 68*x^4 + 124*x^3 + 68*x^2 + 9*x + 28, x^41 + 76*x^39 + 32*x^38 + 94*x^37 + 44*x^35 + 32*x^34 + 77*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 94*x^5 + 12*x^3 + 32*x^2 + 97*x + 64, x^41 + 76*x^39 + 64*x^38 + 62*x^37 + 96*x^36 + 44*x^35 + 64*x^34 + 109*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 62*x^5 + 96*x^4 + 12*x^3 + 64*x^2 + x + 32, x^41 + 76*x^39 + 8*x^38 + 110*x^37 + 8*x^36 + 12*x^35 + 24*x^34 + 93*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 110*x^5 + 72*x^4 + 108*x^3 + 88*x^2 + 113*x + 24, x^41 + 76*x^39 + 120*x^38 + 30*x^37 + 72*x^36 + 108*x^35 + 72*x^34 + 77*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 30*x^5 + 8*x^4 + 76*x^3 + 8*x^2 + 97*x + 56, x^41 + 76*x^39 + 76*x^38 + 6*x^37 + 84*x^36 + 92*x^35 + 84*x^34 + 53*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 70*x^5 + 116*x^4 + 60*x^3 + 52*x^2 + 9*x + 44, x^41 + 76*x^39 + 24*x^38 + 126*x^37 + 8*x^36 + 108*x^35 + 40*x^34 + 109*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 126*x^5 + 72*x^4 + 76*x^3 + 104*x^2 + x + 120, x^41 + 76*x^39 + 116*x^38 + 70*x^37 + 44*x^36 + 92*x^35 + 108*x^34 + 117*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 6*x^5 + 12*x^4 + 60*x^3 + 12*x^2 + 73*x + 84, x^41 + 76*x^39 + 92*x^38 + 38*x^37 + 36*x^36 + 28*x^35 + 4*x^34 + 85*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 102*x^5 + 68*x^4 + 124*x^3 + 100*x^2 + 41*x + 28, x^41 + 76*x^39 + 100*x^38 + 6*x^37 + 60*x^36 + 28*x^35 + 60*x^34 + 117*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 70*x^5 + 28*x^4 + 124*x^3 + 92*x^2 + 73*x + 4, x^41 + 76*x^39 + 24*x^38 + 46*x^37 + 120*x^36 + 76*x^35 + 72*x^34 + 93*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 46*x^5 + 56*x^4 + 44*x^3 + 8*x^2 + 113*x + 104, x^41 + 76*x^39 + 92*x^38 + 38*x^37 + 100*x^36 + 92*x^35 + 68*x^34 + 21*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 102*x^5 + 4*x^4 + 60*x^3 + 36*x^2 + 105*x + 28, x^41 + 76*x^39 + 64*x^38 + 94*x^37 + 96*x^36 + 44*x^35 + 77*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 94*x^5 + 96*x^4 + 12*x^3 + 97*x + 96, x^41 + 76*x^39 + 80*x^38 + 94*x^37 + 80*x^36 + 108*x^35 + 48*x^34 + 13*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 94*x^5 + 80*x^4 + 76*x^3 + 48*x^2 + 33*x + 48, x^41 + 76*x^39 + 116*x^38 + 118*x^37 + 60*x^36 + 124*x^35 + 12*x^34 + 37*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 54*x^5 + 28*x^4 + 92*x^3 + 44*x^2 + 121*x + 36, x^41 + 76*x^39 + 36*x^38 + 54*x^37 + 12*x^36 + 60*x^35 + 28*x^34 + 37*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 118*x^5 + 108*x^4 + 28*x^3 + 60*x^2 + 121*x + 20, x^41 + 76*x^39 + 52*x^38 + 118*x^37 + 28*x^36 + 60*x^35 + 76*x^34 + 101*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 54*x^5 + 124*x^4 + 28*x^3 + 108*x^2 + 57*x + 68, x^41 + 76*x^39 + 56*x^38 + 126*x^37 + 72*x^36 + 44*x^35 + 8*x^34 + 45*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 126*x^5 + 8*x^4 + 12*x^3 + 72*x^2 + 65*x + 56, x^41 + 76*x^39 + 44*x^38 + 6*x^37 + 52*x^36 + 92*x^35 + 116*x^34 + 53*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 70*x^5 + 84*x^4 + 60*x^3 + 84*x^2 + 9*x + 76, x^41 + 76*x^39 + 96*x^38 + 110*x^37 + 80*x^36 + 12*x^35 + 93*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 110*x^5 + 80*x^4 + 108*x^3 + 113*x + 80, x^41 + 76*x^39 + 68*x^38 + 86*x^37 + 44*x^36 + 60*x^35 + 60*x^34 + 5*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 22*x^5 + 12*x^4 + 28*x^3 + 92*x^2 + 89*x + 52, x^41 + 76*x^39 + 16*x^38 + 14*x^37 + 32*x^36 + 12*x^35 + 16*x^34 + 61*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 14*x^5 + 32*x^4 + 108*x^3 + 16*x^2 + 81*x + 64, x^41 + 76*x^39 + 76*x^38 + 38*x^37 + 84*x^36 + 28*x^35 + 84*x^34 + 85*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 102*x^5 + 116*x^4 + 124*x^3 + 52*x^2 + 41*x + 44, x^41 + 76*x^39 + 76*x^38 + 6*x^37 + 52*x^36 + 28*x^35 + 84*x^34 + 117*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 70*x^5 + 84*x^4 + 124*x^3 + 52*x^2 + 73*x + 76, x^41 + 76*x^39 + 24*x^38 + 94*x^37 + 8*x^36 + 44*x^35 + 40*x^34 + 77*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 94*x^5 + 72*x^4 + 12*x^3 + 104*x^2 + 97*x + 120, x^41 + 76*x^39 + 112*x^38 + 30*x^37 + 80*x^36 + 108*x^35 + 80*x^34 + 77*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 30*x^5 + 80*x^4 + 76*x^3 + 80*x^2 + 97*x + 112, x^41 + 76*x^39 + 64*x^38 + 126*x^37 + 108*x^35 + 64*x^34 + 109*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 126*x^5 + 76*x^3 + 64*x^2 + x, x^41 + 76*x^39 + 94*x^37 + 64*x^36 + 108*x^35 + 64*x^34 + 13*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 94*x^5 + 64*x^4 + 76*x^3 + 64*x^2 + 33*x, x^41 + 76*x^39 + 12*x^38 + 6*x^37 + 52*x^36 + 92*x^35 + 84*x^34 + 53*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 70*x^5 + 84*x^4 + 60*x^3 + 52*x^2 + 9*x + 12, x^41 + 76*x^39 + 64*x^38 + 94*x^37 + 64*x^36 + 108*x^35 + 13*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 94*x^5 + 64*x^4 + 76*x^3 + 33*x, x^41 + 76*x^39 + 8*x^38 + 78*x^37 + 72*x^36 + 12*x^35 + 88*x^34 + 125*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 78*x^5 + 8*x^4 + 108*x^3 + 24*x^2 + 17*x + 24, x^41 + 76*x^39 + 56*x^38 + 30*x^37 + 72*x^36 + 44*x^35 + 72*x^34 + 13*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 30*x^5 + 8*x^4 + 12*x^3 + 8*x^2 + 33*x + 120, x^41 + 76*x^39 + 120*x^38 + 78*x^37 + 88*x^36 + 76*x^35 + 40*x^34 + 61*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 78*x^5 + 24*x^4 + 44*x^3 + 104*x^2 + 81*x + 72, x^41 + 76*x^39 + 104*x^38 + 94*x^37 + 24*x^36 + 44*x^35 + 24*x^34 + 77*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 94*x^5 + 88*x^4 + 12*x^3 + 88*x^2 + 97*x + 40, x^41 + 76*x^39 + 44*x^38 + 102*x^37 + 84*x^36 + 92*x^35 + 116*x^34 + 85*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 38*x^5 + 116*x^4 + 60*x^3 + 84*x^2 + 41*x + 44, x^41 + 76*x^39 + 120*x^38 + 126*x^37 + 72*x^36 + 108*x^35 + 8*x^34 + 109*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 126*x^5 + 8*x^4 + 76*x^3 + 72*x^2 + x + 120, x^41 + 76*x^39 + 24*x^38 + 30*x^37 + 104*x^36 + 108*x^35 + 40*x^34 + 77*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 30*x^5 + 40*x^4 + 76*x^3 + 104*x^2 + 97*x + 24, x^41 + 76*x^39 + 104*x^38 + 30*x^37 + 56*x^36 + 44*x^35 + 88*x^34 + 13*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 30*x^5 + 120*x^4 + 12*x^3 + 24*x^2 + 33*x + 72, x^41 + 76*x^39 + 112*x^38 + 14*x^37 + 64*x^36 + 76*x^35 + 112*x^34 + 125*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 14*x^5 + 64*x^4 + 44*x^3 + 112*x^2 + 17*x + 96, x^41 + 76*x^39 + 20*x^38 + 70*x^37 + 108*x^36 + 92*x^35 + 12*x^34 + 117*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 6*x^5 + 76*x^4 + 60*x^3 + 44*x^2 + 73*x + 84, x^41 + 76*x^39 + 48*x^38 + 94*x^37 + 112*x^36 + 108*x^35 + 80*x^34 + 13*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 94*x^5 + 112*x^4 + 76*x^3 + 80*x^2 + 33*x + 16, x^41 + 76*x^39 + 96*x^38 + 62*x^37 + 64*x^36 + 108*x^35 + 96*x^34 + 45*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 62*x^5 + 64*x^4 + 76*x^3 + 96*x^2 + 65*x, x^41 + 76*x^39 + 124*x^38 + 102*x^37 + 4*x^36 + 92*x^35 + 36*x^34 + 85*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 38*x^5 + 36*x^4 + 60*x^3 + 4*x^2 + 41*x + 124, x^41 + 76*x^39 + 72*x^38 + 78*x^37 + 104*x^36 + 12*x^35 + 88*x^34 + 125*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 78*x^5 + 40*x^4 + 108*x^3 + 24*x^2 + 17*x + 56, x^41 + 76*x^39 + 52*x^38 + 38*x^37 + 76*x^36 + 28*x^35 + 108*x^34 + 85*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 102*x^5 + 44*x^4 + 124*x^3 + 12*x^2 + 41*x + 116, x^41 + 76*x^39 + 104*x^38 + 14*x^37 + 8*x^36 + 12*x^35 + 56*x^34 + 61*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 14*x^5 + 72*x^4 + 108*x^3 + 120*x^2 + 81*x + 24, x^41 + 76*x^39 + 76*x^38 + 6*x^37 + 116*x^36 + 92*x^35 + 20*x^34 + 53*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 70*x^5 + 20*x^4 + 60*x^3 + 116*x^2 + 9*x + 76, x^41 + 76*x^39 + 92*x^38 + 118*x^37 + 20*x^36 + 60*x^35 + 36*x^34 + 101*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 54*x^5 + 52*x^4 + 28*x^3 + 4*x^2 + 57*x + 12, x^41 + 76*x^39 + 56*x^38 + 46*x^37 + 56*x^36 + 76*x^35 + 104*x^34 + 93*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 46*x^5 + 120*x^4 + 44*x^3 + 40*x^2 + 113*x + 104, x^41 + 76*x^39 + 88*x^38 + 46*x^37 + 24*x^36 + 12*x^35 + 8*x^34 + 29*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 46*x^5 + 88*x^4 + 108*x^3 + 72*x^2 + 49*x + 72, x^41 + 76*x^39 + 108*x^38 + 102*x^37 + 20*x^36 + 92*x^35 + 52*x^34 + 85*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 38*x^5 + 52*x^4 + 60*x^3 + 20*x^2 + 41*x + 108, x^41 + 76*x^39 + 96*x^38 + 30*x^37 + 96*x^36 + 108*x^35 + 96*x^34 + 77*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 30*x^5 + 96*x^4 + 76*x^3 + 96*x^2 + 97*x + 96, x^41 + 76*x^39 + 84*x^38 + 22*x^37 + 124*x^36 + 60*x^35 + 108*x^34 + 69*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 86*x^5 + 92*x^4 + 28*x^3 + 12*x^2 + 25*x + 36, x^41 + 76*x^39 + 48*x^38 + 126*x^37 + 16*x^36 + 108*x^35 + 80*x^34 + 109*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 126*x^5 + 16*x^4 + 76*x^3 + 80*x^2 + x + 112, x^41 + 76*x^39 + 84*x^38 + 118*x^37 + 92*x^36 + 60*x^35 + 108*x^34 + 101*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 54*x^5 + 60*x^4 + 28*x^3 + 12*x^2 + 57*x + 68, x^41 + 76*x^39 + 100*x^38 + 22*x^37 + 76*x^36 + 124*x^35 + 92*x^34 + 5*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 86*x^5 + 44*x^4 + 92*x^3 + 124*x^2 + 89*x + 84, x^41 + 76*x^39 + 4*x^38 + 70*x^37 + 92*x^36 + 28*x^35 + 28*x^34 + 53*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 6*x^5 + 60*x^4 + 124*x^3 + 60*x^2 + 9*x + 100, x^41 + 76*x^39 + 24*x^38 + 30*x^37 + 104*x^36 + 44*x^35 + 104*x^34 + 13*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 30*x^5 + 40*x^4 + 12*x^3 + 40*x^2 + 33*x + 88, x^41 + 76*x^39 + 28*x^38 + 86*x^37 + 116*x^36 + 124*x^35 + 36*x^34 + 69*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 22*x^5 + 20*x^4 + 92*x^3 + 4*x^2 + 25*x + 108, x^41 + 76*x^39 + 36*x^38 + 38*x^37 + 124*x^36 + 92*x^35 + 124*x^34 + 21*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 102*x^5 + 92*x^4 + 60*x^3 + 28*x^2 + 105*x + 68, x^41 + 76*x^39 + 20*x^38 + 6*x^37 + 108*x^36 + 92*x^35 + 12*x^34 + 53*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 70*x^5 + 76*x^4 + 60*x^3 + 44*x^2 + 9*x + 84, x^41 + 76*x^39 + 8*x^38 + 62*x^37 + 88*x^36 + 108*x^35 + 56*x^34 + 45*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 62*x^5 + 24*x^4 + 76*x^3 + 120*x^2 + 65*x + 40, x^41 + 76*x^39 + 48*x^38 + 30*x^37 + 80*x^36 + 108*x^35 + 16*x^34 + 77*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 30*x^5 + 80*x^4 + 76*x^3 + 16*x^2 + 97*x + 112, x^41 + 76*x^39 + 96*x^38 + 30*x^37 + 64*x^36 + 44*x^35 + 96*x^34 + 13*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 30*x^5 + 64*x^4 + 12*x^3 + 96*x^2 + 33*x, x^41 + 76*x^39 + 12*x^38 + 22*x^37 + 36*x^36 + 124*x^35 + 116*x^34 + 5*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 86*x^5 + 68*x^4 + 92*x^3 + 84*x^2 + 89*x + 124, x^41 + 76*x^39 + 60*x^38 + 70*x^37 + 100*x^36 + 92*x^35 + 100*x^34 + 117*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 6*x^5 + 4*x^4 + 60*x^3 + 68*x^2 + 73*x + 28, x^41 + 76*x^39 + 20*x^38 + 54*x^37 + 124*x^36 + 124*x^35 + 44*x^34 + 101*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 118*x^5 + 92*x^4 + 92*x^3 + 76*x^2 + 57*x + 36, x^41 + 76*x^39 + 20*x^38 + 86*x^37 + 124*x^36 + 60*x^35 + 44*x^34 + 5*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 22*x^5 + 92*x^4 + 28*x^3 + 76*x^2 + 89*x + 36, x^41 + 76*x^39 + 84*x^38 + 6*x^37 + 108*x^36 + 28*x^35 + 12*x^34 + 117*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 70*x^5 + 76*x^4 + 124*x^3 + 44*x^2 + 73*x + 20, x^41 + 76*x^39 + 64*x^38 + 14*x^37 + 112*x^36 + 12*x^35 + 96*x^34 + 61*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 14*x^5 + 112*x^4 + 108*x^3 + 96*x^2 + 81*x + 112, x^41 + 76*x^39 + 4*x^38 + 22*x^37 + 12*x^36 + 60*x^35 + 60*x^34 + 69*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 86*x^5 + 108*x^4 + 28*x^3 + 92*x^2 + 25*x + 20, x^41 + 76*x^39 + 104*x^38 + 78*x^37 + 40*x^36 + 76*x^35 + 56*x^34 + 61*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 78*x^5 + 104*x^4 + 44*x^3 + 120*x^2 + 81*x + 120, x^41 + 76*x^39 + 4*x^38 + 118*x^37 + 44*x^36 + 124*x^35 + 124*x^34 + 37*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 54*x^5 + 12*x^4 + 92*x^3 + 28*x^2 + 121*x + 52, x^41 + 76*x^39 + 100*x^38 + 6*x^37 + 60*x^36 + 92*x^35 + 124*x^34 + 53*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 70*x^5 + 28*x^4 + 60*x^3 + 28*x^2 + 9*x + 68, x^41 + 76*x^39 + 48*x^38 + 46*x^37 + 32*x^36 + 76*x^35 + 48*x^34 + 93*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 46*x^5 + 32*x^4 + 44*x^3 + 48*x^2 + 113*x, x^41 + 76*x^39 + 16*x^38 + 14*x^37 + 76*x^35 + 16*x^34 + 125*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 14*x^5 + 44*x^3 + 16*x^2 + 17*x + 96, x^41 + 76*x^39 + 24*x^38 + 46*x^37 + 88*x^36 + 12*x^35 + 72*x^34 + 29*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 46*x^5 + 24*x^4 + 108*x^3 + 8*x^2 + 49*x + 8, x^41 + 76*x^39 + 80*x^38 + 14*x^37 + 96*x^36 + 76*x^35 + 16*x^34 + 125*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 14*x^5 + 96*x^4 + 44*x^3 + 16*x^2 + 17*x + 64, x^41 + 76*x^39 + 124*x^38 + 6*x^37 + 100*x^36 + 92*x^35 + 36*x^34 + 53*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 70*x^5 + 4*x^4 + 60*x^3 + 4*x^2 + 9*x + 28, x^41 + 76*x^39 + 64*x^38 + 126*x^37 + 96*x^36 + 44*x^35 + 64*x^34 + 45*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 126*x^5 + 96*x^4 + 12*x^3 + 64*x^2 + 65*x + 32, x^41 + 76*x^39 + 108*x^38 + 22*x^37 + 4*x^36 + 124*x^35 + 20*x^34 + 5*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 86*x^5 + 36*x^4 + 92*x^3 + 116*x^2 + 89*x + 28, x^41 + 76*x^39 + 68*x^38 + 102*x^37 + 60*x^36 + 92*x^35 + 28*x^34 + 85*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 38*x^5 + 28*x^4 + 60*x^3 + 60*x^2 + 41*x + 68, x^41 + 76*x^39 + 8*x^38 + 78*x^37 + 40*x^36 + 76*x^35 + 88*x^34 + 61*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 78*x^5 + 104*x^4 + 44*x^3 + 24*x^2 + 81*x + 56, x^41 + 76*x^39 + 56*x^38 + 62*x^37 + 40*x^36 + 108*x^35 + 8*x^34 + 45*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 62*x^5 + 104*x^4 + 76*x^3 + 72*x^2 + 65*x + 88, x^41 + 76*x^39 + 104*x^38 + 14*x^37 + 72*x^36 + 76*x^35 + 120*x^34 + 125*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 14*x^5 + 8*x^4 + 44*x^3 + 56*x^2 + 17*x + 24, x^41 + 76*x^39 + 124*x^38 + 54*x^37 + 52*x^36 + 60*x^35 + 4*x^34 + 37*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 118*x^5 + 84*x^4 + 28*x^3 + 100*x^2 + 121*x + 108, x^41 + 76*x^39 + 88*x^38 + 30*x^37 + 72*x^36 + 44*x^35 + 104*x^34 + 13*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 30*x^5 + 8*x^4 + 12*x^3 + 40*x^2 + 33*x + 56, x^41 + 76*x^39 + 24*x^38 + 126*x^37 + 72*x^36 + 108*x^35 + 40*x^34 + 109*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 126*x^5 + 8*x^4 + 76*x^3 + 104*x^2 + x + 56, x^41 + 76*x^39 + 4*x^38 + 86*x^37 + 76*x^36 + 124*x^35 + 124*x^34 + 69*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 22*x^5 + 44*x^4 + 92*x^3 + 28*x^2 + 25*x + 20, x^41 + 76*x^39 + 124*x^38 + 6*x^37 + 4*x^36 + 92*x^35 + 100*x^34 + 53*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 70*x^5 + 36*x^4 + 60*x^3 + 68*x^2 + 9*x + 60, x^41 + 76*x^39 + 44*x^38 + 54*x^37 + 36*x^36 + 60*x^35 + 20*x^34 + 37*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 118*x^5 + 68*x^4 + 28*x^3 + 116*x^2 + 121*x + 60, x^41 + 76*x^39 + 92*x^38 + 86*x^37 + 52*x^36 + 124*x^35 + 100*x^34 + 69*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 22*x^5 + 84*x^4 + 92*x^3 + 68*x^2 + 25*x + 44, x^41 + 76*x^39 + 20*x^38 + 70*x^37 + 12*x^36 + 28*x^35 + 12*x^34 + 53*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 6*x^5 + 108*x^4 + 124*x^3 + 44*x^2 + 9*x + 52, x^41 + 76*x^39 + 108*x^38 + 118*x^37 + 36*x^36 + 60*x^35 + 84*x^34 + 101*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 54*x^5 + 68*x^4 + 28*x^3 + 52*x^2 + 57*x + 60, x^41 + 76*x^39 + 94*x^37 + 32*x^36 + 44*x^35 + 64*x^34 + 77*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 94*x^5 + 32*x^4 + 12*x^3 + 64*x^2 + 97*x + 32, x^41 + 76*x^39 + 64*x^38 + 78*x^37 + 48*x^36 + 76*x^35 + 32*x^34 + 61*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 78*x^5 + 48*x^4 + 44*x^3 + 32*x^2 + 81*x + 112, x^41 + 76*x^39 + 64*x^38 + 94*x^37 + 32*x^36 + 44*x^35 + 77*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 94*x^5 + 32*x^4 + 12*x^3 + 97*x + 32, x^41 + 76*x^39 + 24*x^38 + 78*x^37 + 88*x^36 + 12*x^35 + 8*x^34 + 125*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 78*x^5 + 24*x^4 + 108*x^3 + 72*x^2 + 17*x + 72, x^41 + 76*x^39 + 80*x^38 + 78*x^37 + 96*x^36 + 76*x^35 + 16*x^34 + 61*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 78*x^5 + 96*x^4 + 44*x^3 + 16*x^2 + 81*x + 64, x^41 + 76*x^39 + 76*x^38 + 102*x^37 + 52*x^36 + 92*x^35 + 84*x^34 + 85*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 38*x^5 + 84*x^4 + 60*x^3 + 52*x^2 + 41*x + 76, x^41 + 76*x^39 + 4*x^38 + 86*x^37 + 108*x^36 + 60*x^35 + 124*x^34 + 5*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 22*x^5 + 76*x^4 + 28*x^3 + 28*x^2 + 89*x + 116, x^41 + 76*x^39 + 72*x^38 + 126*x^37 + 24*x^36 + 44*x^35 + 56*x^34 + 45*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 126*x^5 + 88*x^4 + 12*x^3 + 120*x^2 + 65*x + 40, x^41 + 76*x^39 + 76*x^38 + 38*x^37 + 20*x^36 + 28*x^35 + 84*x^34 + 85*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 102*x^5 + 52*x^4 + 124*x^3 + 52*x^2 + 41*x + 108, x^41 + 76*x^39 + 44*x^38 + 118*x^37 + 4*x^36 + 60*x^35 + 84*x^34 + 101*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 54*x^5 + 36*x^4 + 28*x^3 + 52*x^2 + 57*x + 28, x^41 + 76*x^39 + 56*x^38 + 30*x^37 + 8*x^36 + 108*x^35 + 8*x^34 + 77*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 30*x^5 + 72*x^4 + 76*x^3 + 72*x^2 + 97*x + 120, x^41 + 76*x^39 + 116*x^38 + 118*x^37 + 28*x^36 + 124*x^35 + 76*x^34 + 37*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 54*x^5 + 124*x^4 + 92*x^3 + 108*x^2 + 121*x + 4, x^41 + 76*x^39 + 28*x^38 + 118*x^37 + 52*x^36 + 60*x^35 + 36*x^34 + 101*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 54*x^5 + 84*x^4 + 28*x^3 + 4*x^2 + 57*x + 44, x^41 + 76*x^39 + 52*x^38 + 22*x^37 + 60*x^36 + 60*x^35 + 76*x^34 + 69*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 86*x^5 + 28*x^4 + 28*x^3 + 108*x^2 + 25*x + 36, x^41 + 76*x^39 + 104*x^38 + 30*x^37 + 120*x^36 + 108*x^35 + 24*x^34 + 77*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 30*x^5 + 56*x^4 + 76*x^3 + 88*x^2 + 97*x + 72, x^41 + 76*x^39 + 94*x^37 + 44*x^35 + 77*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 94*x^5 + 12*x^3 + 97*x, x^41 + 76*x^39 + 44*x^38 + 102*x^37 + 84*x^36 + 28*x^35 + 52*x^34 + 21*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 38*x^5 + 116*x^4 + 124*x^3 + 20*x^2 + 105*x + 108, x^41 + 76*x^39 + 32*x^38 + 62*x^37 + 44*x^35 + 96*x^34 + 109*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 62*x^5 + 12*x^3 + 96*x^2 + x, x^41 + 76*x^39 + 88*x^38 + 30*x^37 + 8*x^36 + 108*x^35 + 40*x^34 + 77*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 30*x^5 + 72*x^4 + 76*x^3 + 104*x^2 + 97*x + 56, x^41 + 76*x^39 + 56*x^38 + 14*x^37 + 88*x^36 + 76*x^35 + 104*x^34 + 125*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 14*x^5 + 24*x^4 + 44*x^3 + 40*x^2 + 17*x + 72, x^41 + 76*x^39 + 112*x^38 + 110*x^37 + 64*x^36 + 12*x^35 + 112*x^34 + 93*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 110*x^5 + 64*x^4 + 108*x^3 + 112*x^2 + 113*x + 96, x^41 + 76*x^39 + 100*x^38 + 118*x^37 + 76*x^36 + 124*x^35 + 28*x^34 + 37*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 54*x^5 + 44*x^4 + 92*x^3 + 60*x^2 + 121*x + 20, x^41 + 76*x^39 + 12*x^38 + 22*x^37 + 68*x^36 + 60*x^35 + 116*x^34 + 69*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 86*x^5 + 100*x^4 + 28*x^3 + 84*x^2 + 25*x + 92, x^41 + 76*x^39 + 96*x^38 + 126*x^37 + 64*x^36 + 108*x^35 + 96*x^34 + 109*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 126*x^5 + 64*x^4 + 76*x^3 + 96*x^2 + x, x^41 + 76*x^39 + 80*x^38 + 30*x^37 + 112*x^36 + 108*x^35 + 112*x^34 + 77*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 30*x^5 + 112*x^4 + 76*x^3 + 112*x^2 + 97*x + 80, x^41 + 76*x^39 + 104*x^38 + 110*x^37 + 8*x^36 + 76*x^35 + 56*x^34 + 29*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 110*x^5 + 72*x^4 + 44*x^3 + 120*x^2 + 49*x + 24, x^41 + 76*x^39 + 104*x^38 + 78*x^37 + 8*x^36 + 12*x^35 + 56*x^34 + 125*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 78*x^5 + 72*x^4 + 108*x^3 + 120*x^2 + 17*x + 24, x^41 + 76*x^39 + 64*x^38 + 78*x^37 + 112*x^36 + 76*x^35 + 32*x^34 + 61*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 78*x^5 + 112*x^4 + 44*x^3 + 32*x^2 + 81*x + 48, x^41 + 76*x^39 + 116*x^38 + 38*x^37 + 44*x^36 + 92*x^35 + 44*x^34 + 21*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 102*x^5 + 12*x^4 + 60*x^3 + 76*x^2 + 105*x + 20, x^41 + 76*x^39 + 32*x^38 + 46*x^37 + 48*x^36 + 76*x^35 + 64*x^34 + 93*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 46*x^5 + 48*x^4 + 44*x^3 + 64*x^2 + 113*x + 112, x^41 + 76*x^39 + 92*x^38 + 22*x^37 + 84*x^36 + 124*x^35 + 36*x^34 + 5*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 86*x^5 + 116*x^4 + 92*x^3 + 4*x^2 + 89*x + 76, x^41 + 76*x^39 + 52*x^38 + 102*x^37 + 76*x^36 + 28*x^35 + 108*x^34 + 21*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 38*x^5 + 44*x^4 + 124*x^3 + 12*x^2 + 105*x + 116, x^41 + 76*x^39 + 44*x^38 + 70*x^37 + 116*x^36 + 92*x^35 + 116*x^34 + 117*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 6*x^5 + 20*x^4 + 60*x^3 + 84*x^2 + 73*x + 12, x^41 + 76*x^39 + 76*x^38 + 86*x^37 + 4*x^36 + 60*x^35 + 52*x^34 + 5*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 22*x^5 + 36*x^4 + 28*x^3 + 20*x^2 + 89*x + 28, x^41 + 76*x^39 + 60*x^38 + 38*x^37 + 100*x^36 + 28*x^35 + 100*x^34 + 85*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 102*x^5 + 4*x^4 + 124*x^3 + 68*x^2 + 41*x + 28, x^41 + 76*x^39 + 52*x^38 + 6*x^37 + 76*x^36 + 28*x^35 + 44*x^34 + 117*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 70*x^5 + 44*x^4 + 124*x^3 + 76*x^2 + 73*x + 52, x^41 + 76*x^39 + 88*x^38 + 30*x^37 + 40*x^36 + 108*x^35 + 104*x^34 + 77*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 30*x^5 + 104*x^4 + 76*x^3 + 40*x^2 + 97*x + 88, x^41 + 76*x^39 + 52*x^38 + 70*x^37 + 76*x^36 + 28*x^35 + 44*x^34 + 53*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 6*x^5 + 44*x^4 + 124*x^3 + 76*x^2 + 9*x + 52, x^41 + 76*x^39 + 46*x^37 + 112*x^36 + 76*x^35 + 32*x^34 + 93*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 46*x^5 + 112*x^4 + 44*x^3 + 32*x^2 + 113*x + 112, x^41 + 76*x^39 + 88*x^38 + 94*x^37 + 104*x^36 + 108*x^35 + 104*x^34 + 13*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 94*x^5 + 40*x^4 + 76*x^3 + 40*x^2 + 33*x + 24, x^41 + 76*x^39 + 96*x^38 + 14*x^37 + 80*x^36 + 12*x^35 + 64*x^34 + 61*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 14*x^5 + 80*x^4 + 108*x^3 + 64*x^2 + 81*x + 16, x^41 + 76*x^39 + 88*x^38 + 78*x^37 + 24*x^36 + 76*x^35 + 8*x^34 + 61*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 78*x^5 + 88*x^4 + 44*x^3 + 72*x^2 + 81*x + 72, x^41 + 76*x^39 + 28*x^38 + 54*x^37 + 52*x^36 + 60*x^35 + 36*x^34 + 37*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 118*x^5 + 84*x^4 + 28*x^3 + 4*x^2 + 121*x + 44, x^41 + 76*x^39 + 120*x^38 + 46*x^37 + 24*x^36 + 12*x^35 + 40*x^34 + 29*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 46*x^5 + 88*x^4 + 108*x^3 + 104*x^2 + 49*x + 8, x^41 + 76*x^39 + 60*x^38 + 86*x^37 + 20*x^36 + 60*x^35 + 68*x^34 + 5*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 22*x^5 + 52*x^4 + 28*x^3 + 36*x^2 + 89*x + 12, x^41 + 76*x^39 + 92*x^38 + 70*x^37 + 68*x^36 + 28*x^35 + 4*x^34 + 53*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 6*x^5 + 100*x^4 + 124*x^3 + 100*x^2 + 9*x + 124, x^41 + 76*x^39 + 32*x^38 + 94*x^37 + 96*x^36 + 44*x^35 + 96*x^34 + 77*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 94*x^5 + 96*x^4 + 12*x^3 + 96*x^2 + 97*x + 32, x^41 + 76*x^39 + 120*x^38 + 46*x^37 + 56*x^36 + 12*x^35 + 104*x^34 + 29*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 46*x^5 + 120*x^4 + 108*x^3 + 40*x^2 + 49*x + 40, x^41 + 76*x^39 + 60*x^38 + 38*x^37 + 68*x^36 + 28*x^35 + 36*x^34 + 85*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 102*x^5 + 100*x^4 + 124*x^3 + 4*x^2 + 41*x + 124, x^41 + 76*x^39 + 104*x^38 + 14*x^37 + 72*x^36 + 12*x^35 + 56*x^34 + 61*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 14*x^5 + 8*x^4 + 108*x^3 + 120*x^2 + 81*x + 88, x^41 + 76*x^39 + 44*x^38 + 86*x^37 + 100*x^36 + 60*x^35 + 84*x^34 + 5*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 22*x^5 + 4*x^4 + 28*x^3 + 52*x^2 + 89*x + 60, x^41 + 76*x^39 + 116*x^38 + 54*x^37 + 60*x^36 + 60*x^35 + 76*x^34 + 37*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 118*x^5 + 28*x^4 + 28*x^3 + 108*x^2 + 121*x + 100, x^41 + 76*x^39 + 52*x^38 + 54*x^37 + 124*x^36 + 124*x^35 + 76*x^34 + 101*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 118*x^5 + 92*x^4 + 92*x^3 + 108*x^2 + 57*x + 100, x^41 + 76*x^39 + 48*x^38 + 46*x^37 + 12*x^35 + 48*x^34 + 29*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 46*x^5 + 108*x^3 + 48*x^2 + 49*x + 32, x^41 + 76*x^39 + 84*x^38 + 38*x^37 + 12*x^36 + 28*x^35 + 12*x^34 + 85*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 102*x^5 + 108*x^4 + 124*x^3 + 44*x^2 + 41*x + 116, x^41 + 76*x^39 + 40*x^38 + 62*x^37 + 120*x^36 + 108*x^35 + 24*x^34 + 45*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 62*x^5 + 56*x^4 + 76*x^3 + 88*x^2 + 65*x + 8, x^41 + 76*x^39 + 8*x^38 + 14*x^37 + 72*x^36 + 12*x^35 + 88*x^34 + 61*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 14*x^5 + 8*x^4 + 108*x^3 + 24*x^2 + 81*x + 24, x^41 + 76*x^39 + 8*x^38 + 126*x^37 + 56*x^36 + 108*x^35 + 120*x^34 + 109*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 126*x^5 + 120*x^4 + 76*x^3 + 56*x^2 + x + 8, x^41 + 76*x^39 + 120*x^38 + 14*x^37 + 120*x^36 + 12*x^35 + 40*x^34 + 61*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 14*x^5 + 56*x^4 + 108*x^3 + 104*x^2 + 81*x + 40, x^41 + 76*x^39 + 124*x^38 + 22*x^37 + 84*x^36 + 124*x^35 + 68*x^34 + 5*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 86*x^5 + 116*x^4 + 92*x^3 + 36*x^2 + 89*x + 12, x^41 + 76*x^39 + 56*x^38 + 62*x^37 + 40*x^36 + 44*x^35 + 72*x^34 + 109*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 62*x^5 + 104*x^4 + 12*x^3 + 8*x^2 + x + 24, x^41 + 76*x^39 + 48*x^38 + 78*x^37 + 32*x^36 + 12*x^35 + 48*x^34 + 125*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 78*x^5 + 32*x^4 + 108*x^3 + 48*x^2 + 17*x, x^41 + 76*x^39 + 16*x^38 + 110*x^37 + 12*x^35 + 16*x^34 + 93*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 110*x^5 + 108*x^3 + 16*x^2 + 113*x + 96, x^41 + 76*x^39 + 116*x^38 + 102*x^37 + 12*x^36 + 28*x^35 + 44*x^34 + 21*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 38*x^5 + 108*x^4 + 124*x^3 + 76*x^2 + 105*x + 52, x^41 + 76*x^39 + 80*x^38 + 110*x^37 + 96*x^36 + 12*x^35 + 16*x^34 + 93*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 110*x^5 + 96*x^4 + 108*x^3 + 16*x^2 + 113*x + 64, x^41 + 76*x^39 + 12*x^38 + 6*x^37 + 20*x^36 + 28*x^35 + 84*x^34 + 117*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 70*x^5 + 52*x^4 + 124*x^3 + 52*x^2 + 73*x + 44, x^41 + 76*x^39 + 8*x^38 + 94*x^37 + 24*x^36 + 44*x^35 + 56*x^34 + 77*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 94*x^5 + 88*x^4 + 12*x^3 + 120*x^2 + 97*x + 104, x^41 + 76*x^39 + 48*x^38 + 62*x^37 + 16*x^36 + 44*x^35 + 16*x^34 + 109*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 62*x^5 + 16*x^4 + 12*x^3 + 16*x^2 + x + 48, x^41 + 76*x^39 + 8*x^38 + 30*x^37 + 88*x^36 + 44*x^35 + 56*x^34 + 13*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 30*x^5 + 24*x^4 + 12*x^3 + 120*x^2 + 33*x + 40, x^41 + 76*x^39 + 40*x^38 + 14*x^37 + 72*x^36 + 12*x^35 + 120*x^34 + 61*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 14*x^5 + 8*x^4 + 108*x^3 + 56*x^2 + 81*x + 88, x^41 + 76*x^39 + 24*x^38 + 30*x^37 + 8*x^36 + 108*x^35 + 104*x^34 + 77*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 30*x^5 + 72*x^4 + 76*x^3 + 40*x^2 + 97*x + 56, x^41 + 76*x^39 + 52*x^38 + 118*x^37 + 124*x^36 + 124*x^35 + 76*x^34 + 37*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 54*x^5 + 92*x^4 + 92*x^3 + 108*x^2 + 121*x + 100, x^41 + 76*x^39 + 32*x^38 + 78*x^37 + 16*x^36 + 76*x^35 + 64*x^34 + 61*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 78*x^5 + 16*x^4 + 44*x^3 + 64*x^2 + 81*x + 16, x^41 + 76*x^39 + 62*x^37 + 32*x^36 + 44*x^35 + 109*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 62*x^5 + 32*x^4 + 12*x^3 + x + 96, x^41 + 76*x^39 + 76*x^38 + 102*x^37 + 84*x^36 + 28*x^35 + 84*x^34 + 21*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 38*x^5 + 116*x^4 + 124*x^3 + 52*x^2 + 105*x + 44, x^41 + 76*x^39 + 108*x^38 + 54*x^37 + 100*x^36 + 60*x^35 + 84*x^34 + 37*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 118*x^5 + 4*x^4 + 28*x^3 + 52*x^2 + 121*x + 124, x^41 + 76*x^39 + 96*x^38 + 14*x^37 + 48*x^36 + 12*x^35 + 61*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 14*x^5 + 48*x^4 + 108*x^3 + 81*x + 112, x^41 + 76*x^39 + 112*x^38 + 14*x^37 + 64*x^36 + 12*x^35 + 48*x^34 + 61*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 14*x^5 + 64*x^4 + 108*x^3 + 48*x^2 + 81*x + 32, x^41 + 76*x^39 + 68*x^38 + 54*x^37 + 76*x^36 + 124*x^35 + 124*x^34 + 101*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 118*x^5 + 44*x^4 + 92*x^3 + 28*x^2 + 57*x + 84, x^41 + 76*x^39 + 96*x^38 + 94*x^37 + 32*x^36 + 108*x^35 + 96*x^34 + 13*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 94*x^5 + 32*x^4 + 76*x^3 + 96*x^2 + 33*x + 32, x^41 + 76*x^39 + 76*x^38 + 54*x^37 + 100*x^36 + 124*x^35 + 116*x^34 + 101*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 118*x^5 + 4*x^4 + 92*x^3 + 84*x^2 + 57*x + 124, x^41 + 76*x^39 + 40*x^38 + 126*x^37 + 24*x^36 + 108*x^35 + 88*x^34 + 109*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 126*x^5 + 88*x^4 + 76*x^3 + 24*x^2 + x + 40, x^41 + 76*x^39 + 100*x^38 + 6*x^37 + 92*x^36 + 28*x^35 + 124*x^34 + 117*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 70*x^5 + 60*x^4 + 124*x^3 + 28*x^2 + 73*x + 36, x^41 + 76*x^39 + 48*x^38 + 46*x^37 + 64*x^36 + 76*x^35 + 112*x^34 + 93*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 46*x^5 + 64*x^4 + 44*x^3 + 112*x^2 + 113*x + 32, x^41 + 76*x^39 + 36*x^38 + 22*x^37 + 76*x^36 + 124*x^35 + 28*x^34 + 5*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 86*x^5 + 44*x^4 + 92*x^3 + 60*x^2 + 89*x + 84, x^41 + 76*x^39 + 100*x^38 + 54*x^37 + 76*x^36 + 60*x^35 + 92*x^34 + 37*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 118*x^5 + 44*x^4 + 28*x^3 + 124*x^2 + 121*x + 84, x^41 + 76*x^39 + 60*x^38 + 22*x^37 + 20*x^36 + 60*x^35 + 68*x^34 + 69*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 86*x^5 + 52*x^4 + 28*x^3 + 36*x^2 + 25*x + 12, x^41 + 76*x^39 + 12*x^38 + 54*x^37 + 4*x^36 + 60*x^35 + 52*x^34 + 37*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 118*x^5 + 36*x^4 + 28*x^3 + 20*x^2 + 121*x + 92, x^41 + 76*x^39 + 88*x^38 + 94*x^37 + 104*x^36 + 44*x^35 + 40*x^34 + 77*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 94*x^5 + 40*x^4 + 12*x^3 + 104*x^2 + 97*x + 88, x^41 + 76*x^39 + 108*x^38 + 86*x^37 + 36*x^36 + 60*x^35 + 20*x^34 + 5*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 22*x^5 + 68*x^4 + 28*x^3 + 116*x^2 + 89*x + 124, x^41 + 76*x^39 + 20*x^38 + 102*x^37 + 76*x^36 + 28*x^35 + 76*x^34 + 21*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 38*x^5 + 44*x^4 + 124*x^3 + 108*x^2 + 105*x + 52, x^41 + 76*x^39 + 80*x^38 + 14*x^37 + 32*x^36 + 12*x^35 + 80*x^34 + 61*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 14*x^5 + 32*x^4 + 108*x^3 + 80*x^2 + 81*x + 64, x^41 + 76*x^39 + 12*x^38 + 6*x^37 + 116*x^36 + 28*x^35 + 20*x^34 + 117*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 70*x^5 + 20*x^4 + 124*x^3 + 116*x^2 + 73*x + 12, x^41 + 76*x^39 + 104*x^38 + 14*x^37 + 8*x^36 + 76*x^35 + 120*x^34 + 125*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 14*x^5 + 72*x^4 + 44*x^3 + 56*x^2 + 17*x + 88, x^41 + 76*x^39 + 28*x^38 + 70*x^37 + 36*x^36 + 92*x^35 + 68*x^34 + 117*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 6*x^5 + 68*x^4 + 60*x^3 + 36*x^2 + 73*x + 28, x^41 + 76*x^39 + 76*x^38 + 6*x^37 + 20*x^36 + 92*x^35 + 84*x^34 + 53*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 70*x^5 + 52*x^4 + 60*x^3 + 52*x^2 + 9*x + 108, x^41 + 76*x^39 + 80*x^38 + 94*x^37 + 16*x^36 + 44*x^35 + 112*x^34 + 77*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 94*x^5 + 16*x^4 + 12*x^3 + 112*x^2 + 97*x + 48, x^41 + 76*x^39 + 32*x^38 + 62*x^37 + 108*x^35 + 32*x^34 + 45*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 62*x^5 + 76*x^3 + 32*x^2 + 65*x + 64, x^41 + 76*x^39 + 116*x^38 + 38*x^37 + 12*x^36 + 92*x^35 + 108*x^34 + 21*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 102*x^5 + 108*x^4 + 60*x^3 + 12*x^2 + 105*x + 116, x^41 + 76*x^39 + 36*x^38 + 6*x^37 + 124*x^36 + 92*x^35 + 60*x^34 + 53*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 70*x^5 + 92*x^4 + 60*x^3 + 92*x^2 + 9*x + 4, x^41 + 76*x^39 + 72*x^38 + 14*x^37 + 8*x^36 + 76*x^35 + 88*x^34 + 125*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 14*x^5 + 72*x^4 + 44*x^3 + 24*x^2 + 17*x + 24, x^41 + 76*x^39 + 48*x^38 + 46*x^37 + 96*x^36 + 12*x^35 + 112*x^34 + 29*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 46*x^5 + 96*x^4 + 108*x^3 + 112*x^2 + 49*x, x^41 + 76*x^39 + 100*x^38 + 54*x^37 + 76*x^36 + 124*x^35 + 28*x^34 + 101*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 118*x^5 + 44*x^4 + 92*x^3 + 60*x^2 + 57*x + 20, x^41 + 76*x^39 + 108*x^38 + 6*x^37 + 20*x^36 + 28*x^35 + 52*x^34 + 117*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 70*x^5 + 52*x^4 + 124*x^3 + 20*x^2 + 73*x + 108, x^41 + 76*x^39 + 96*x^38 + 14*x^37 + 112*x^36 + 12*x^35 + 61*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 14*x^5 + 112*x^4 + 108*x^3 + 81*x + 48, x^41 + 76*x^39 + 56*x^38 + 30*x^37 + 40*x^36 + 44*x^35 + 8*x^34 + 13*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 30*x^5 + 104*x^4 + 12*x^3 + 72*x^2 + 33*x + 88, x^41 + 76*x^39 + 32*x^38 + 14*x^37 + 16*x^36 + 12*x^35 + 61*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 14*x^5 + 16*x^4 + 108*x^3 + 81*x + 80, x^41 + 76*x^39 + 120*x^38 + 14*x^37 + 120*x^36 + 76*x^35 + 104*x^34 + 125*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 14*x^5 + 56*x^4 + 44*x^3 + 40*x^2 + 17*x + 104, x^41 + 76*x^39 + 112*x^38 + 94*x^37 + 48*x^36 + 44*x^35 + 80*x^34 + 77*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 94*x^5 + 48*x^4 + 12*x^3 + 80*x^2 + 97*x + 16, x^41 + 76*x^39 + 44*x^38 + 22*x^37 + 100*x^36 + 124*x^35 + 20*x^34 + 5*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 86*x^5 + 4*x^4 + 92*x^3 + 116*x^2 + 89*x + 124, x^41 + 76*x^39 + 116*x^38 + 102*x^37 + 76*x^36 + 28*x^35 + 44*x^34 + 21*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 38*x^5 + 44*x^4 + 124*x^3 + 76*x^2 + 105*x + 116, x^41 + 76*x^39 + 52*x^38 + 38*x^37 + 76*x^36 + 92*x^35 + 44*x^34 + 21*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 102*x^5 + 44*x^4 + 60*x^3 + 76*x^2 + 105*x + 52, x^41 + 76*x^39 + 124*x^38 + 86*x^37 + 20*x^36 + 124*x^35 + 68*x^34 + 69*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 22*x^5 + 52*x^4 + 92*x^3 + 36*x^2 + 25*x + 76, x^41 + 76*x^39 + 48*x^38 + 78*x^37 + 96*x^36 + 76*x^35 + 112*x^34 + 61*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 78*x^5 + 96*x^4 + 44*x^3 + 112*x^2 + 81*x, x^41 + 76*x^39 + 48*x^38 + 126*x^37 + 16*x^36 + 44*x^35 + 16*x^34 + 45*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 126*x^5 + 16*x^4 + 12*x^3 + 16*x^2 + 65*x + 48, x^41 + 76*x^39 + 68*x^38 + 118*x^37 + 44*x^36 + 60*x^35 + 124*x^34 + 101*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 54*x^5 + 12*x^4 + 28*x^3 + 28*x^2 + 57*x + 116, x^41 + 76*x^39 + 28*x^38 + 118*x^37 + 116*x^36 + 60*x^35 + 36*x^34 + 101*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 54*x^5 + 20*x^4 + 28*x^3 + 4*x^2 + 57*x + 108, x^41 + 76*x^39 + 32*x^38 + 30*x^37 + 32*x^36 + 44*x^35 + 96*x^34 + 13*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 30*x^5 + 32*x^4 + 12*x^3 + 96*x^2 + 33*x + 96, x^41 + 76*x^39 + 32*x^38 + 30*x^37 + 44*x^35 + 32*x^34 + 13*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 30*x^5 + 12*x^3 + 32*x^2 + 33*x + 64, x^41 + 76*x^39 + 96*x^38 + 62*x^37 + 96*x^36 + 44*x^35 + 96*x^34 + 109*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 62*x^5 + 96*x^4 + 12*x^3 + 96*x^2 + x + 96, x^41 + 76*x^39 + 52*x^38 + 22*x^37 + 28*x^36 + 124*x^35 + 76*x^34 + 5*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 86*x^5 + 124*x^4 + 92*x^3 + 108*x^2 + 89*x + 68, x^41 + 76*x^39 + 52*x^38 + 86*x^37 + 60*x^36 + 60*x^35 + 76*x^34 + 5*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 22*x^5 + 28*x^4 + 28*x^3 + 108*x^2 + 89*x + 36, x^41 + 76*x^39 + 108*x^38 + 6*x^37 + 84*x^36 + 28*x^35 + 52*x^34 + 117*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 70*x^5 + 116*x^4 + 124*x^3 + 20*x^2 + 73*x + 44, x^41 + 76*x^39 + 40*x^38 + 110*x^37 + 72*x^36 + 76*x^35 + 120*x^34 + 29*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 110*x^5 + 8*x^4 + 44*x^3 + 56*x^2 + 49*x + 88, x^41 + 76*x^39 + 96*x^38 + 94*x^37 + 108*x^35 + 32*x^34 + 13*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 94*x^5 + 76*x^3 + 32*x^2 + 33*x, x^41 + 76*x^39 + 20*x^38 + 118*x^37 + 28*x^36 + 60*x^35 + 44*x^34 + 101*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 54*x^5 + 124*x^4 + 28*x^3 + 76*x^2 + 57*x + 4, x^41 + 76*x^39 + 20*x^38 + 102*x^37 + 108*x^36 + 28*x^35 + 12*x^34 + 21*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 38*x^5 + 76*x^4 + 124*x^3 + 44*x^2 + 105*x + 84, x^41 + 76*x^39 + 24*x^38 + 62*x^37 + 40*x^36 + 108*x^35 + 104*x^34 + 45*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 62*x^5 + 104*x^4 + 76*x^3 + 40*x^2 + 65*x + 24, x^41 + 76*x^39 + 16*x^38 + 30*x^37 + 80*x^36 + 108*x^35 + 112*x^34 + 77*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 30*x^5 + 80*x^4 + 76*x^3 + 112*x^2 + 97*x + 48, x^41 + 76*x^39 + 120*x^38 + 94*x^37 + 40*x^36 + 108*x^35 + 8*x^34 + 13*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 94*x^5 + 104*x^4 + 76*x^3 + 72*x^2 + 33*x + 24, x^41 + 76*x^39 + 76*x^38 + 54*x^37 + 36*x^36 + 124*x^35 + 116*x^34 + 101*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 118*x^5 + 68*x^4 + 92*x^3 + 84*x^2 + 57*x + 60, x^41 + 76*x^39 + 8*x^38 + 110*x^37 + 72*x^36 + 76*x^35 + 88*x^34 + 29*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 110*x^5 + 8*x^4 + 44*x^3 + 24*x^2 + 49*x + 24, x^41 + 76*x^39 + 32*x^38 + 126*x^37 + 32*x^36 + 44*x^35 + 32*x^34 + 45*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 126*x^5 + 32*x^4 + 12*x^3 + 32*x^2 + 65*x + 32, x^41 + 76*x^39 + 56*x^38 + 110*x^37 + 120*x^36 + 76*x^35 + 104*x^34 + 29*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 110*x^5 + 56*x^4 + 44*x^3 + 40*x^2 + 49*x + 40, x^41 + 76*x^39 + 8*x^38 + 14*x^37 + 40*x^36 + 12*x^35 + 24*x^34 + 61*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 14*x^5 + 104*x^4 + 108*x^3 + 88*x^2 + 81*x + 120, x^41 + 76*x^39 + 68*x^38 + 118*x^37 + 108*x^36 + 60*x^35 + 124*x^34 + 101*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 54*x^5 + 76*x^4 + 28*x^3 + 28*x^2 + 57*x + 52, x^41 + 76*x^39 + 120*x^38 + 110*x^37 + 56*x^36 + 76*x^35 + 40*x^34 + 29*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 110*x^5 + 120*x^4 + 44*x^3 + 104*x^2 + 49*x + 104, x^41 + 76*x^39 + 80*x^38 + 30*x^37 + 80*x^36 + 44*x^35 + 112*x^34 + 13*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 30*x^5 + 80*x^4 + 12*x^3 + 112*x^2 + 33*x + 112, x^41 + 76*x^39 + 14*x^37 + 16*x^36 + 12*x^35 + 96*x^34 + 61*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 14*x^5 + 16*x^4 + 108*x^3 + 96*x^2 + 81*x + 16, x^41 + 76*x^39 + 124*x^38 + 54*x^37 + 84*x^36 + 124*x^35 + 4*x^34 + 101*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 118*x^5 + 116*x^4 + 92*x^3 + 100*x^2 + 57*x + 76, x^41 + 76*x^39 + 112*x^38 + 46*x^37 + 32*x^36 + 76*x^35 + 112*x^34 + 93*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 46*x^5 + 32*x^4 + 44*x^3 + 112*x^2 + 113*x, x^41 + 76*x^39 + 80*x^38 + 14*x^37 + 76*x^35 + 80*x^34 + 125*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 14*x^5 + 44*x^3 + 80*x^2 + 17*x + 96, x^41 + 76*x^39 + 116*x^38 + 70*x^37 + 12*x^36 + 28*x^35 + 108*x^34 + 53*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 6*x^5 + 108*x^4 + 124*x^3 + 12*x^2 + 9*x + 116, x^41 + 76*x^39 + 116*x^38 + 86*x^37 + 60*x^36 + 60*x^35 + 12*x^34 + 5*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 22*x^5 + 28*x^4 + 28*x^3 + 44*x^2 + 89*x + 36, x^41 + 76*x^39 + 44*x^38 + 102*x^37 + 52*x^36 + 28*x^35 + 116*x^34 + 21*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 38*x^5 + 84*x^4 + 124*x^3 + 84*x^2 + 105*x + 76, x^41 + 76*x^39 + 120*x^38 + 14*x^37 + 88*x^36 + 76*x^35 + 40*x^34 + 125*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 14*x^5 + 24*x^4 + 44*x^3 + 104*x^2 + 17*x + 72, x^41 + 76*x^39 + 124*x^38 + 102*x^37 + 100*x^36 + 28*x^35 + 36*x^34 + 21*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 38*x^5 + 4*x^4 + 124*x^3 + 4*x^2 + 105*x + 28, x^41 + 76*x^39 + 92*x^38 + 70*x^37 + 4*x^36 + 92*x^35 + 68*x^34 + 117*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 6*x^5 + 36*x^4 + 60*x^3 + 36*x^2 + 73*x + 124, x^41 + 76*x^39 + 92*x^38 + 6*x^37 + 4*x^36 + 92*x^35 + 68*x^34 + 53*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 70*x^5 + 36*x^4 + 60*x^3 + 36*x^2 + 9*x + 124, x^41 + 76*x^39 + 28*x^38 + 6*x^37 + 36*x^36 + 28*x^35 + 4*x^34 + 117*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 70*x^5 + 68*x^4 + 124*x^3 + 100*x^2 + 73*x + 92, x^41 + 76*x^39 + 84*x^38 + 118*x^37 + 92*x^36 + 124*x^35 + 44*x^34 + 37*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 54*x^5 + 60*x^4 + 92*x^3 + 76*x^2 + 121*x + 4, x^41 + 76*x^39 + 52*x^38 + 86*x^37 + 92*x^36 + 124*x^35 + 76*x^34 + 69*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 22*x^5 + 60*x^4 + 92*x^3 + 108*x^2 + 25*x + 4, x^41 + 76*x^39 + 126*x^37 + 32*x^36 + 44*x^35 + 45*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 126*x^5 + 32*x^4 + 12*x^3 + 65*x + 96, x^41 + 76*x^39 + 108*x^38 + 70*x^37 + 84*x^36 + 28*x^35 + 52*x^34 + 53*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 6*x^5 + 116*x^4 + 124*x^3 + 20*x^2 + 9*x + 44, x^41 + 76*x^39 + 48*x^38 + 126*x^37 + 80*x^36 + 44*x^35 + 16*x^34 + 45*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 126*x^5 + 80*x^4 + 12*x^3 + 16*x^2 + 65*x + 112, x^41 + 76*x^39 + 72*x^38 + 62*x^37 + 56*x^36 + 108*x^35 + 56*x^34 + 45*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 62*x^5 + 120*x^4 + 76*x^3 + 120*x^2 + 65*x + 8, x^41 + 76*x^39 + 108*x^38 + 86*x^37 + 100*x^36 + 60*x^35 + 20*x^34 + 5*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 22*x^5 + 4*x^4 + 28*x^3 + 116*x^2 + 89*x + 60, x^41 + 76*x^39 + 80*x^38 + 30*x^37 + 48*x^36 + 44*x^35 + 48*x^34 + 13*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 30*x^5 + 48*x^4 + 12*x^3 + 48*x^2 + 33*x + 80, x^41 + 76*x^39 + 40*x^38 + 30*x^37 + 88*x^36 + 108*x^35 + 24*x^34 + 77*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 30*x^5 + 24*x^4 + 76*x^3 + 88*x^2 + 97*x + 40, x^41 + 76*x^39 + 8*x^38 + 30*x^37 + 88*x^36 + 108*x^35 + 120*x^34 + 77*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 30*x^5 + 24*x^4 + 76*x^3 + 56*x^2 + 97*x + 104, x^41 + 76*x^39 + 100*x^38 + 6*x^37 + 28*x^36 + 92*x^35 + 60*x^34 + 53*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 70*x^5 + 124*x^4 + 60*x^3 + 92*x^2 + 9*x + 36, x^41 + 76*x^39 + 76*x^38 + 86*x^37 + 36*x^36 + 60*x^35 + 116*x^34 + 5*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 22*x^5 + 68*x^4 + 28*x^3 + 84*x^2 + 89*x + 60, x^41 + 76*x^39 + 36*x^38 + 118*x^37 + 44*x^36 + 60*x^35 + 92*x^34 + 101*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 54*x^5 + 12*x^4 + 28*x^3 + 124*x^2 + 57*x + 52, x^41 + 76*x^39 + 72*x^38 + 14*x^37 + 8*x^36 + 12*x^35 + 24*x^34 + 61*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 14*x^5 + 72*x^4 + 108*x^3 + 88*x^2 + 81*x + 88, x^41 + 76*x^39 + 124*x^38 + 6*x^37 + 68*x^36 + 28*x^35 + 36*x^34 + 117*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 70*x^5 + 100*x^4 + 124*x^3 + 4*x^2 + 73*x + 60, x^41 + 76*x^39 + 56*x^38 + 62*x^37 + 104*x^36 + 44*x^35 + 72*x^34 + 109*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 62*x^5 + 40*x^4 + 12*x^3 + 8*x^2 + x + 88, x^41 + 76*x^39 + 60*x^38 + 70*x^37 + 68*x^36 + 28*x^35 + 100*x^34 + 53*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 6*x^5 + 100*x^4 + 124*x^3 + 68*x^2 + 9*x + 60, x^41 + 76*x^39 + 36*x^38 + 86*x^37 + 108*x^36 + 124*x^35 + 92*x^34 + 69*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 22*x^5 + 76*x^4 + 92*x^3 + 124*x^2 + 25*x + 116, x^41 + 76*x^39 + 16*x^38 + 30*x^37 + 48*x^36 + 44*x^35 + 112*x^34 + 13*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 30*x^5 + 48*x^4 + 12*x^3 + 112*x^2 + 33*x + 80, x^41 + 76*x^39 + 56*x^38 + 62*x^37 + 8*x^36 + 44*x^35 + 8*x^34 + 109*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 62*x^5 + 72*x^4 + 12*x^3 + 72*x^2 + x + 120, x^41 + 76*x^39 + 56*x^38 + 14*x^37 + 120*x^36 + 12*x^35 + 104*x^34 + 61*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 14*x^5 + 56*x^4 + 108*x^3 + 40*x^2 + 81*x + 40, x^41 + 76*x^39 + 72*x^38 + 46*x^37 + 104*x^36 + 76*x^35 + 88*x^34 + 93*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 46*x^5 + 40*x^4 + 44*x^3 + 24*x^2 + 113*x + 56, x^41 + 76*x^39 + 48*x^38 + 126*x^37 + 112*x^36 + 108*x^35 + 16*x^34 + 109*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 126*x^5 + 112*x^4 + 76*x^3 + 16*x^2 + x + 80, x^41 + 76*x^39 + 36*x^38 + 86*x^37 + 44*x^36 + 124*x^35 + 92*x^34 + 69*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 22*x^5 + 12*x^4 + 92*x^3 + 124*x^2 + 25*x + 52, x^41 + 76*x^39 + 60*x^38 + 102*x^37 + 68*x^36 + 28*x^35 + 36*x^34 + 21*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 38*x^5 + 100*x^4 + 124*x^3 + 4*x^2 + 105*x + 124, x^41 + 76*x^39 + 88*x^38 + 14*x^37 + 56*x^36 + 12*x^35 + 8*x^34 + 61*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 14*x^5 + 120*x^4 + 108*x^3 + 72*x^2 + 81*x + 40, x^41 + 76*x^39 + 44*x^38 + 38*x^37 + 116*x^36 + 92*x^35 + 52*x^34 + 21*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 102*x^5 + 20*x^4 + 60*x^3 + 20*x^2 + 105*x + 76, x^41 + 76*x^39 + 28*x^38 + 6*x^37 + 36*x^36 + 92*x^35 + 68*x^34 + 53*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 70*x^5 + 68*x^4 + 60*x^3 + 36*x^2 + 9*x + 28, x^41 + 76*x^39 + 20*x^38 + 38*x^37 + 12*x^36 + 92*x^35 + 12*x^34 + 21*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 102*x^5 + 108*x^4 + 60*x^3 + 44*x^2 + 105*x + 52, x^41 + 76*x^39 + 88*x^38 + 126*x^37 + 104*x^36 + 44*x^35 + 104*x^34 + 45*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 126*x^5 + 40*x^4 + 12*x^3 + 40*x^2 + 65*x + 24, x^41 + 76*x^39 + 124*x^38 + 86*x^37 + 116*x^36 + 124*x^35 + 4*x^34 + 69*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 22*x^5 + 20*x^4 + 92*x^3 + 100*x^2 + 25*x + 44, x^41 + 76*x^39 + 84*x^38 + 102*x^37 + 12*x^36 + 28*x^35 + 12*x^34 + 21*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 38*x^5 + 108*x^4 + 124*x^3 + 44*x^2 + 105*x + 116, x^41 + 76*x^39 + 96*x^38 + 126*x^37 + 32*x^36 + 108*x^35 + 32*x^34 + 109*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 126*x^5 + 32*x^4 + 76*x^3 + 32*x^2 + x + 96, x^41 + 76*x^39 + 32*x^38 + 30*x^37 + 96*x^36 + 44*x^35 + 96*x^34 + 13*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 30*x^5 + 96*x^4 + 12*x^3 + 96*x^2 + 33*x + 32, x^41 + 76*x^39 + 28*x^38 + 118*x^37 + 20*x^36 + 124*x^35 + 36*x^34 + 37*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 54*x^5 + 52*x^4 + 92*x^3 + 4*x^2 + 121*x + 76, x^41 + 76*x^39 + 32*x^38 + 126*x^37 + 108*x^35 + 32*x^34 + 109*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 126*x^5 + 76*x^3 + 32*x^2 + x + 64, x^41 + 76*x^39 + 32*x^38 + 126*x^37 + 96*x^36 + 108*x^35 + 96*x^34 + 109*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 126*x^5 + 96*x^4 + 76*x^3 + 96*x^2 + x + 32, x^41 + 76*x^39 + 20*x^38 + 22*x^37 + 92*x^36 + 124*x^35 + 44*x^34 + 5*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 86*x^5 + 60*x^4 + 92*x^3 + 76*x^2 + 89*x + 68, x^41 + 76*x^39 + 116*x^38 + 38*x^37 + 76*x^36 + 92*x^35 + 108*x^34 + 21*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 102*x^5 + 44*x^4 + 60*x^3 + 12*x^2 + 105*x + 52, x^41 + 76*x^39 + 72*x^38 + 94*x^37 + 24*x^36 + 44*x^35 + 120*x^34 + 77*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 94*x^5 + 88*x^4 + 12*x^3 + 56*x^2 + 97*x + 104, x^41 + 76*x^39 + 4*x^38 + 38*x^37 + 92*x^36 + 28*x^35 + 92*x^34 + 85*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 102*x^5 + 60*x^4 + 124*x^3 + 124*x^2 + 41*x + 36, x^41 + 76*x^39 + 16*x^38 + 110*x^37 + 96*x^36 + 12*x^35 + 80*x^34 + 93*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 110*x^5 + 96*x^4 + 108*x^3 + 80*x^2 + 113*x + 64, x^41 + 76*x^39 + 48*x^38 + 126*x^37 + 80*x^36 + 108*x^35 + 80*x^34 + 109*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 126*x^5 + 80*x^4 + 76*x^3 + 80*x^2 + x + 48, x^41 + 76*x^39 + 44*x^38 + 38*x^37 + 20*x^36 + 92*x^35 + 116*x^34 + 21*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 102*x^5 + 52*x^4 + 60*x^3 + 84*x^2 + 105*x + 108, x^41 + 76*x^39 + 40*x^38 + 78*x^37 + 104*x^36 + 76*x^35 + 120*x^34 + 61*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 78*x^5 + 40*x^4 + 44*x^3 + 56*x^2 + 81*x + 56, x^41 + 76*x^39 + 104*x^38 + 30*x^37 + 24*x^36 + 108*x^35 + 88*x^34 + 77*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 30*x^5 + 88*x^4 + 76*x^3 + 24*x^2 + 97*x + 104, x^41 + 76*x^39 + 44*x^38 + 54*x^37 + 100*x^36 + 124*x^35 + 84*x^34 + 101*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 118*x^5 + 4*x^4 + 92*x^3 + 52*x^2 + 57*x + 60, x^41 + 76*x^39 + 80*x^38 + 126*x^37 + 80*x^36 + 108*x^35 + 112*x^34 + 109*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 126*x^5 + 80*x^4 + 76*x^3 + 112*x^2 + x + 112, x^41 + 76*x^39 + 36*x^38 + 6*x^37 + 60*x^36 + 28*x^35 + 124*x^34 + 117*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 70*x^5 + 28*x^4 + 124*x^3 + 28*x^2 + 73*x + 4, x^41 + 76*x^39 + 124*x^38 + 70*x^37 + 68*x^36 + 28*x^35 + 36*x^34 + 53*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 6*x^5 + 100*x^4 + 124*x^3 + 4*x^2 + 9*x + 60, x^41 + 76*x^39 + 126*x^37 + 44*x^35 + 64*x^34 + 45*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 126*x^5 + 12*x^3 + 64*x^2 + 65*x + 64, x^41 + 76*x^39 + 56*x^38 + 62*x^37 + 72*x^36 + 44*x^35 + 8*x^34 + 109*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 62*x^5 + 8*x^4 + 12*x^3 + 72*x^2 + x + 56, x^41 + 76*x^39 + 88*x^38 + 62*x^37 + 72*x^36 + 44*x^35 + 40*x^34 + 109*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 62*x^5 + 8*x^4 + 12*x^3 + 104*x^2 + x + 120, x^41 + 76*x^39 + 64*x^38 + 62*x^37 + 32*x^36 + 108*x^35 + 45*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 62*x^5 + 32*x^4 + 76*x^3 + 65*x + 32, x^41 + 76*x^39 + 32*x^38 + 110*x^37 + 48*x^36 + 76*x^35 + 64*x^34 + 29*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 110*x^5 + 48*x^4 + 44*x^3 + 64*x^2 + 49*x + 112, x^41 + 76*x^39 + 20*x^38 + 118*x^37 + 60*x^36 + 124*x^35 + 44*x^34 + 37*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 54*x^5 + 28*x^4 + 92*x^3 + 76*x^2 + 121*x + 100, x^41 + 76*x^39 + 12*x^38 + 6*x^37 + 52*x^36 + 28*x^35 + 20*x^34 + 117*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 70*x^5 + 84*x^4 + 124*x^3 + 116*x^2 + 73*x + 76, x^41 + 76*x^39 + 72*x^38 + 126*x^37 + 120*x^36 + 44*x^35 + 120*x^34 + 45*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 126*x^5 + 56*x^4 + 12*x^3 + 56*x^2 + 65*x + 8, x^41 + 76*x^39 + 96*x^38 + 94*x^37 + 96*x^36 + 108*x^35 + 96*x^34 + 13*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 94*x^5 + 96*x^4 + 76*x^3 + 96*x^2 + 33*x + 96, x^41 + 76*x^39 + 16*x^38 + 94*x^37 + 16*x^36 + 108*x^35 + 112*x^34 + 13*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 94*x^5 + 16*x^4 + 76*x^3 + 112*x^2 + 33*x + 112, x^41 + 76*x^39 + 52*x^38 + 38*x^37 + 12*x^36 + 92*x^35 + 44*x^34 + 21*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 102*x^5 + 108*x^4 + 60*x^3 + 76*x^2 + 105*x + 116, x^41 + 76*x^39 + 4*x^38 + 54*x^37 + 76*x^36 + 124*x^35 + 60*x^34 + 101*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 118*x^5 + 44*x^4 + 92*x^3 + 92*x^2 + 57*x + 84, x^41 + 76*x^39 + 44*x^38 + 6*x^37 + 116*x^36 + 92*x^35 + 116*x^34 + 53*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 70*x^5 + 20*x^4 + 60*x^3 + 84*x^2 + 9*x + 12, x^41 + 76*x^39 + 92*x^38 + 38*x^37 + 100*x^36 + 28*x^35 + 4*x^34 + 85*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 102*x^5 + 4*x^4 + 124*x^3 + 100*x^2 + 41*x + 92, x^41 + 76*x^39 + 72*x^38 + 14*x^37 + 72*x^36 + 76*x^35 + 88*x^34 + 125*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 14*x^5 + 8*x^4 + 44*x^3 + 24*x^2 + 17*x + 88, x^41 + 76*x^39 + 116*x^38 + 70*x^37 + 12*x^36 + 92*x^35 + 44*x^34 + 117*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 6*x^5 + 108*x^4 + 60*x^3 + 76*x^2 + 73*x + 52, x^41 + 76*x^39 + 80*x^38 + 62*x^37 + 16*x^36 + 44*x^35 + 48*x^34 + 109*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 62*x^5 + 16*x^4 + 12*x^3 + 48*x^2 + x + 112, x^41 + 76*x^39 + 28*x^38 + 86*x^37 + 52*x^36 + 124*x^35 + 36*x^34 + 69*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 22*x^5 + 84*x^4 + 92*x^3 + 4*x^2 + 25*x + 44, x^41 + 76*x^39 + 92*x^38 + 86*x^37 + 20*x^36 + 60*x^35 + 100*x^34 + 5*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 22*x^5 + 52*x^4 + 28*x^3 + 68*x^2 + 89*x + 76, x^41 + 76*x^39 + 48*x^38 + 94*x^37 + 48*x^36 + 108*x^35 + 80*x^34 + 13*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 94*x^5 + 48*x^4 + 76*x^3 + 80*x^2 + 33*x + 80, x^41 + 76*x^39 + 84*x^38 + 118*x^37 + 28*x^36 + 124*x^35 + 44*x^34 + 37*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 54*x^5 + 124*x^4 + 92*x^3 + 76*x^2 + 121*x + 68, x^41 + 76*x^39 + 40*x^38 + 78*x^37 + 40*x^36 + 76*x^35 + 120*x^34 + 61*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 78*x^5 + 104*x^4 + 44*x^3 + 56*x^2 + 81*x + 120, x^41 + 76*x^39 + 120*x^38 + 62*x^37 + 72*x^36 + 108*x^35 + 8*x^34 + 45*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 62*x^5 + 8*x^4 + 76*x^3 + 72*x^2 + 65*x + 120, x^41 + 76*x^39 + 4*x^38 + 102*x^37 + 124*x^36 + 28*x^35 + 28*x^34 + 21*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 38*x^5 + 92*x^4 + 124*x^3 + 60*x^2 + 105*x + 68, x^41 + 76*x^39 + 62*x^37 + 108*x^35 + 45*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 62*x^5 + 76*x^3 + 65*x, x^41 + 76*x^39 + 116*x^38 + 70*x^37 + 76*x^36 + 92*x^35 + 44*x^34 + 117*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 6*x^5 + 44*x^4 + 60*x^3 + 76*x^2 + 73*x + 116, x^41 + 76*x^39 + 88*x^38 + 14*x^37 + 120*x^36 + 76*x^35 + 72*x^34 + 125*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 14*x^5 + 56*x^4 + 44*x^3 + 8*x^2 + 17*x + 40, x^41 + 76*x^39 + 116*x^38 + 6*x^37 + 76*x^36 + 92*x^35 + 44*x^34 + 53*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 70*x^5 + 44*x^4 + 60*x^3 + 76*x^2 + 9*x + 116, x^41 + 76*x^39 + 104*x^38 + 62*x^37 + 56*x^36 + 108*x^35 + 88*x^34 + 45*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 62*x^5 + 120*x^4 + 76*x^3 + 24*x^2 + 65*x + 72, x^41 + 76*x^39 + 4*x^38 + 86*x^37 + 44*x^36 + 60*x^35 + 124*x^34 + 5*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 22*x^5 + 12*x^4 + 28*x^3 + 28*x^2 + 89*x + 52, x^41 + 76*x^39 + 52*x^38 + 38*x^37 + 44*x^36 + 92*x^35 + 108*x^34 + 21*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 102*x^5 + 12*x^4 + 60*x^3 + 12*x^2 + 105*x + 20, x^41 + 76*x^39 + 88*x^38 + 30*x^37 + 40*x^36 + 44*x^35 + 40*x^34 + 13*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 30*x^5 + 104*x^4 + 12*x^3 + 104*x^2 + 33*x + 24, x^41 + 76*x^39 + 60*x^38 + 38*x^37 + 68*x^36 + 92*x^35 + 100*x^34 + 21*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 102*x^5 + 100*x^4 + 60*x^3 + 68*x^2 + 105*x + 60, x^41 + 76*x^39 + 12*x^38 + 118*x^37 + 36*x^36 + 124*x^35 + 52*x^34 + 37*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 54*x^5 + 68*x^4 + 92*x^3 + 20*x^2 + 121*x + 60, x^41 + 76*x^39 + 12*x^38 + 102*x^37 + 20*x^36 + 92*x^35 + 84*x^34 + 85*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 38*x^5 + 52*x^4 + 60*x^3 + 52*x^2 + 41*x + 44, x^41 + 76*x^39 + 30*x^37 + 32*x^36 + 44*x^35 + 64*x^34 + 13*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 30*x^5 + 32*x^4 + 12*x^3 + 64*x^2 + 33*x + 32, x^41 + 76*x^39 + 116*x^38 + 86*x^37 + 28*x^36 + 124*x^35 + 12*x^34 + 69*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 22*x^5 + 124*x^4 + 92*x^3 + 44*x^2 + 25*x + 68, x^41 + 76*x^39 + 88*x^38 + 46*x^37 + 120*x^36 + 12*x^35 + 72*x^34 + 29*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 46*x^5 + 56*x^4 + 108*x^3 + 8*x^2 + 49*x + 40, x^41 + 76*x^39 + 84*x^38 + 6*x^37 + 76*x^36 + 28*x^35 + 76*x^34 + 117*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 70*x^5 + 44*x^4 + 124*x^3 + 108*x^2 + 73*x + 116, x^41 + 76*x^39 + 56*x^38 + 46*x^37 + 88*x^36 + 12*x^35 + 104*x^34 + 29*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 46*x^5 + 24*x^4 + 108*x^3 + 40*x^2 + 49*x + 72, x^41 + 76*x^39 + 68*x^38 + 54*x^37 + 108*x^36 + 60*x^35 + 124*x^34 + 37*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 118*x^5 + 76*x^4 + 28*x^3 + 28*x^2 + 121*x + 52, x^41 + 76*x^39 + 32*x^38 + 110*x^37 + 112*x^36 + 76*x^35 + 64*x^34 + 29*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 110*x^5 + 112*x^4 + 44*x^3 + 64*x^2 + 49*x + 48, x^41 + 76*x^39 + 36*x^38 + 54*x^37 + 108*x^36 + 60*x^35 + 92*x^34 + 37*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 118*x^5 + 76*x^4 + 28*x^3 + 124*x^2 + 121*x + 116, x^41 + 76*x^39 + 48*x^38 + 78*x^37 + 96*x^36 + 12*x^35 + 48*x^34 + 125*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 78*x^5 + 96*x^4 + 108*x^3 + 48*x^2 + 17*x + 64, x^41 + 76*x^39 + 92*x^38 + 22*x^37 + 84*x^36 + 60*x^35 + 100*x^34 + 69*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 86*x^5 + 116*x^4 + 28*x^3 + 68*x^2 + 25*x + 12, x^41 + 76*x^39 + 112*x^38 + 78*x^37 + 32*x^36 + 12*x^35 + 112*x^34 + 125*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 78*x^5 + 32*x^4 + 108*x^3 + 112*x^2 + 17*x, x^41 + 76*x^39 + 80*x^38 + 110*x^37 + 12*x^35 + 80*x^34 + 93*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 110*x^5 + 108*x^3 + 80*x^2 + 113*x + 96, x^41 + 76*x^39 + 120*x^38 + 14*x^37 + 24*x^36 + 76*x^35 + 40*x^34 + 125*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 14*x^5 + 88*x^4 + 44*x^3 + 104*x^2 + 17*x + 8, x^41 + 76*x^39 + 92*x^38 + 86*x^37 + 116*x^36 + 60*x^35 + 36*x^34 + 5*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 22*x^5 + 20*x^4 + 28*x^3 + 4*x^2 + 89*x + 44, x^41 + 76*x^39 + 112*x^38 + 62*x^37 + 16*x^36 + 44*x^35 + 80*x^34 + 109*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 62*x^5 + 16*x^4 + 12*x^3 + 80*x^2 + x + 48, x^41 + 76*x^39 + 40*x^38 + 126*x^37 + 120*x^36 + 108*x^35 + 24*x^34 + 109*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 126*x^5 + 56*x^4 + 76*x^3 + 88*x^2 + x + 8, x^41 + 76*x^39 + 36*x^38 + 6*x^37 + 124*x^36 + 28*x^35 + 124*x^34 + 117*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 70*x^5 + 92*x^4 + 124*x^3 + 28*x^2 + 73*x + 68, x^41 + 76*x^39 + 112*x^38 + 126*x^37 + 48*x^36 + 108*x^35 + 80*x^34 + 109*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 126*x^5 + 48*x^4 + 76*x^3 + 80*x^2 + x + 16, x^41 + 76*x^39 + 88*x^38 + 62*x^37 + 104*x^36 + 108*x^35 + 40*x^34 + 45*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 62*x^5 + 40*x^4 + 76*x^3 + 104*x^2 + 65*x + 88, x^41 + 76*x^39 + 72*x^38 + 110*x^37 + 40*x^36 + 12*x^35 + 24*x^34 + 93*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 110*x^5 + 104*x^4 + 108*x^3 + 88*x^2 + 113*x + 56, x^41 + 76*x^39 + 72*x^38 + 30*x^37 + 120*x^36 + 108*x^35 + 120*x^34 + 77*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 30*x^5 + 56*x^4 + 76*x^3 + 56*x^2 + 97*x + 8, x^41 + 76*x^39 + 30*x^37 + 44*x^35 + 13*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 30*x^5 + 12*x^3 + 33*x, x^41 + 76*x^39 + 120*x^38 + 94*x^37 + 104*x^36 + 108*x^35 + 8*x^34 + 13*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 94*x^5 + 40*x^4 + 76*x^3 + 72*x^2 + 33*x + 88, x^41 + 76*x^39 + 12*x^38 + 38*x^37 + 84*x^36 + 28*x^35 + 20*x^34 + 85*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 102*x^5 + 116*x^4 + 124*x^3 + 116*x^2 + 41*x + 44, x^41 + 76*x^39 + 20*x^38 + 86*x^37 + 92*x^36 + 124*x^35 + 44*x^34 + 69*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 22*x^5 + 60*x^4 + 92*x^3 + 76*x^2 + 25*x + 68, x^41 + 76*x^39 + 36*x^38 + 86*x^37 + 12*x^36 + 60*x^35 + 92*x^34 + 5*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 22*x^5 + 108*x^4 + 28*x^3 + 124*x^2 + 89*x + 84, x^41 + 76*x^39 + 4*x^38 + 102*x^37 + 60*x^36 + 92*x^35 + 92*x^34 + 85*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 38*x^5 + 28*x^4 + 60*x^3 + 124*x^2 + 41*x + 68, x^41 + 76*x^39 + 48*x^38 + 62*x^37 + 112*x^36 + 108*x^35 + 16*x^34 + 45*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 62*x^5 + 112*x^4 + 76*x^3 + 16*x^2 + 65*x + 80, x^41 + 76*x^39 + 108*x^38 + 86*x^37 + 68*x^36 + 60*x^35 + 84*x^34 + 5*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 22*x^5 + 100*x^4 + 28*x^3 + 52*x^2 + 89*x + 28, x^41 + 76*x^39 + 48*x^38 + 30*x^37 + 48*x^36 + 108*x^35 + 80*x^34 + 77*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 30*x^5 + 48*x^4 + 76*x^3 + 80*x^2 + 97*x + 80, x^41 + 76*x^39 + 28*x^38 + 6*x^37 + 68*x^36 + 28*x^35 + 68*x^34 + 117*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 70*x^5 + 100*x^4 + 124*x^3 + 36*x^2 + 73*x + 124, x^41 + 76*x^39 + 24*x^38 + 110*x^37 + 56*x^36 + 76*x^35 + 72*x^34 + 29*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 110*x^5 + 120*x^4 + 44*x^3 + 8*x^2 + 49*x + 40, x^41 + 76*x^39 + 80*x^38 + 14*x^37 + 64*x^36 + 12*x^35 + 16*x^34 + 61*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 14*x^5 + 64*x^4 + 108*x^3 + 16*x^2 + 81*x + 96, x^41 + 76*x^39 + 124*x^38 + 86*x^37 + 84*x^36 + 60*x^35 + 4*x^34 + 5*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 22*x^5 + 116*x^4 + 28*x^3 + 100*x^2 + 89*x + 76, x^41 + 76*x^39 + 84*x^38 + 86*x^37 + 124*x^36 + 124*x^35 + 44*x^34 + 69*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 22*x^5 + 92*x^4 + 92*x^3 + 76*x^2 + 25*x + 100, x^41 + 76*x^39 + 68*x^38 + 22*x^37 + 76*x^36 + 124*x^35 + 60*x^34 + 5*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 86*x^5 + 44*x^4 + 92*x^3 + 92*x^2 + 89*x + 20, x^41 + 76*x^39 + 56*x^38 + 126*x^37 + 8*x^36 + 44*x^35 + 8*x^34 + 45*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 126*x^5 + 72*x^4 + 12*x^3 + 72*x^2 + 65*x + 120, x^41 + 76*x^39 + 88*x^38 + 14*x^37 + 56*x^36 + 76*x^35 + 72*x^34 + 125*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 14*x^5 + 120*x^4 + 44*x^3 + 8*x^2 + 17*x + 104, x^41 + 76*x^39 + 112*x^38 + 110*x^37 + 96*x^36 + 12*x^35 + 48*x^34 + 93*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 110*x^5 + 96*x^4 + 108*x^3 + 48*x^2 + 113*x, x^41 + 76*x^39 + 124*x^38 + 54*x^37 + 20*x^36 + 60*x^35 + 68*x^34 + 37*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 118*x^5 + 52*x^4 + 28*x^3 + 36*x^2 + 121*x + 76, x^41 + 76*x^39 + 124*x^38 + 38*x^37 + 100*x^36 + 92*x^35 + 100*x^34 + 21*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 102*x^5 + 4*x^4 + 60*x^3 + 68*x^2 + 105*x + 92, x^41 + 76*x^39 + 120*x^38 + 94*x^37 + 8*x^36 + 108*x^35 + 72*x^34 + 13*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 94*x^5 + 72*x^4 + 76*x^3 + 8*x^2 + 33*x + 120, x^41 + 76*x^39 + 104*x^38 + 126*x^37 + 120*x^36 + 44*x^35 + 24*x^34 + 45*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 126*x^5 + 56*x^4 + 12*x^3 + 88*x^2 + 65*x + 72, x^41 + 76*x^39 + 16*x^38 + 110*x^37 + 96*x^36 + 76*x^35 + 16*x^34 + 29*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 110*x^5 + 96*x^4 + 44*x^3 + 16*x^2 + 49*x, x^41 + 76*x^39 + 60*x^38 + 102*x^37 + 100*x^36 + 28*x^35 + 100*x^34 + 21*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 38*x^5 + 4*x^4 + 124*x^3 + 68*x^2 + 105*x + 28, x^41 + 76*x^39 + 8*x^38 + 30*x^37 + 120*x^36 + 108*x^35 + 56*x^34 + 77*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 30*x^5 + 56*x^4 + 76*x^3 + 120*x^2 + 97*x + 8, x^41 + 76*x^39 + 108*x^38 + 70*x^37 + 52*x^36 + 28*x^35 + 116*x^34 + 53*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 6*x^5 + 84*x^4 + 124*x^3 + 84*x^2 + 9*x + 12, x^41 + 76*x^39 + 104*x^38 + 46*x^37 + 72*x^36 + 12*x^35 + 120*x^34 + 29*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 46*x^5 + 8*x^4 + 108*x^3 + 56*x^2 + 49*x + 24, x^41 + 76*x^39 + 44*x^38 + 38*x^37 + 52*x^36 + 28*x^35 + 116*x^34 + 85*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 102*x^5 + 84*x^4 + 124*x^3 + 84*x^2 + 41*x + 76, x^41 + 76*x^39 + 40*x^38 + 46*x^37 + 8*x^36 + 12*x^35 + 56*x^34 + 29*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 46*x^5 + 72*x^4 + 108*x^3 + 120*x^2 + 49*x + 88, x^41 + 76*x^39 + 100*x^38 + 102*x^37 + 60*x^36 + 28*x^35 + 124*x^34 + 21*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 38*x^5 + 28*x^4 + 124*x^3 + 28*x^2 + 105*x + 68, x^41 + 76*x^39 + 92*x^38 + 6*x^37 + 100*x^36 + 28*x^35 + 68*x^34 + 117*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 70*x^5 + 4*x^4 + 124*x^3 + 36*x^2 + 73*x + 28, x^41 + 76*x^39 + 124*x^38 + 70*x^37 + 4*x^36 + 92*x^35 + 100*x^34 + 117*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 6*x^5 + 36*x^4 + 60*x^3 + 68*x^2 + 73*x + 60, x^41 + 76*x^39 + 28*x^38 + 54*x^37 + 116*x^36 + 124*x^35 + 100*x^34 + 101*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 118*x^5 + 20*x^4 + 92*x^3 + 68*x^2 + 57*x + 44, x^41 + 76*x^39 + 40*x^38 + 14*x^37 + 8*x^36 + 12*x^35 + 120*x^34 + 61*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 14*x^5 + 72*x^4 + 108*x^3 + 56*x^2 + 81*x + 24, x^41 + 76*x^39 + 64*x^38 + 110*x^37 + 16*x^36 + 76*x^35 + 32*x^34 + 29*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 110*x^5 + 16*x^4 + 44*x^3 + 32*x^2 + 49*x + 16, x^41 + 76*x^39 + 116*x^38 + 118*x^37 + 92*x^36 + 124*x^35 + 76*x^34 + 37*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 54*x^5 + 60*x^4 + 92*x^3 + 108*x^2 + 121*x + 68, x^41 + 76*x^39 + 48*x^38 + 62*x^37 + 112*x^36 + 44*x^35 + 80*x^34 + 109*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 62*x^5 + 112*x^4 + 12*x^3 + 80*x^2 + x + 16, x^41 + 76*x^39 + 62*x^37 + 96*x^36 + 44*x^35 + 109*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 62*x^5 + 96*x^4 + 12*x^3 + x + 32, x^41 + 76*x^39 + 24*x^38 + 62*x^37 + 72*x^36 + 108*x^35 + 40*x^34 + 45*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 62*x^5 + 8*x^4 + 76*x^3 + 104*x^2 + 65*x + 56, x^41 + 76*x^39 + 56*x^38 + 78*x^37 + 24*x^36 + 76*x^35 + 104*x^34 + 61*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 78*x^5 + 88*x^4 + 44*x^3 + 40*x^2 + 81*x + 8, x^41 + 76*x^39 + 84*x^38 + 70*x^37 + 76*x^36 + 92*x^35 + 12*x^34 + 117*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 6*x^5 + 44*x^4 + 60*x^3 + 44*x^2 + 73*x + 52, x^41 + 76*x^39 + 120*x^38 + 94*x^37 + 72*x^36 + 108*x^35 + 72*x^34 + 13*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 94*x^5 + 8*x^4 + 76*x^3 + 8*x^2 + 33*x + 56, x^41 + 76*x^39 + 84*x^38 + 6*x^37 + 76*x^36 + 92*x^35 + 12*x^34 + 53*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 70*x^5 + 44*x^4 + 60*x^3 + 44*x^2 + 9*x + 52, x^41 + 76*x^39 + 32*x^38 + 78*x^37 + 112*x^36 + 76*x^35 + 61*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 78*x^5 + 112*x^4 + 44*x^3 + 81*x + 112, x^41 + 76*x^39 + 104*x^38 + 30*x^37 + 120*x^36 + 44*x^35 + 88*x^34 + 13*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 30*x^5 + 56*x^4 + 12*x^3 + 24*x^2 + 33*x + 8, x^41 + 76*x^39 + 52*x^38 + 6*x^37 + 108*x^36 + 28*x^35 + 108*x^34 + 117*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 70*x^5 + 76*x^4 + 124*x^3 + 12*x^2 + 73*x + 84, x^41 + 76*x^39 + 4*x^38 + 22*x^37 + 108*x^36 + 124*x^35 + 60*x^34 + 5*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 86*x^5 + 76*x^4 + 92*x^3 + 92*x^2 + 89*x + 52, x^41 + 76*x^39 + 92*x^38 + 102*x^37 + 68*x^36 + 28*x^35 + 68*x^34 + 21*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 38*x^5 + 100*x^4 + 124*x^3 + 36*x^2 + 105*x + 60, x^41 + 76*x^39 + 28*x^38 + 70*x^37 + 68*x^36 + 28*x^35 + 68*x^34 + 53*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 6*x^5 + 100*x^4 + 124*x^3 + 36*x^2 + 9*x + 124, x^41 + 76*x^39 + 112*x^38 + 62*x^37 + 48*x^36 + 108*x^35 + 80*x^34 + 45*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 62*x^5 + 48*x^4 + 76*x^3 + 80*x^2 + 65*x + 16, x^41 + 76*x^39 + 126*x^37 + 32*x^36 + 108*x^35 + 64*x^34 + 109*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 126*x^5 + 32*x^4 + 76*x^3 + 64*x^2 + x + 32, x^41 + 76*x^39 + 48*x^38 + 110*x^37 + 12*x^35 + 48*x^34 + 93*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 110*x^5 + 108*x^3 + 48*x^2 + 113*x + 32, x^41 + 76*x^39 + 72*x^38 + 78*x^37 + 40*x^36 + 12*x^35 + 88*x^34 + 125*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 78*x^5 + 104*x^4 + 108*x^3 + 24*x^2 + 17*x + 120, x^41 + 76*x^39 + 120*x^38 + 110*x^37 + 24*x^36 + 76*x^35 + 104*x^34 + 29*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 110*x^5 + 88*x^4 + 44*x^3 + 40*x^2 + 49*x + 72, x^41 + 76*x^39 + 24*x^38 + 126*x^37 + 40*x^36 + 44*x^35 + 40*x^34 + 45*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 126*x^5 + 104*x^4 + 12*x^3 + 104*x^2 + 65*x + 88, x^41 + 76*x^39 + 84*x^38 + 70*x^37 + 76*x^36 + 28*x^35 + 76*x^34 + 53*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 6*x^5 + 44*x^4 + 124*x^3 + 108*x^2 + 9*x + 116, x^41 + 76*x^39 + 76*x^38 + 22*x^37 + 100*x^36 + 60*x^35 + 116*x^34 + 69*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 86*x^5 + 4*x^4 + 28*x^3 + 84*x^2 + 25*x + 124, x^41 + 76*x^39 + 14*x^37 + 80*x^36 + 12*x^35 + 96*x^34 + 61*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 14*x^5 + 80*x^4 + 108*x^3 + 96*x^2 + 81*x + 80, x^41 + 76*x^39 + 12*x^38 + 38*x^37 + 116*x^36 + 28*x^35 + 84*x^34 + 85*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 102*x^5 + 20*x^4 + 124*x^3 + 52*x^2 + 41*x + 76, x^41 + 76*x^39 + 116*x^38 + 54*x^37 + 28*x^36 + 60*x^35 + 12*x^34 + 37*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 118*x^5 + 124*x^4 + 28*x^3 + 44*x^2 + 121*x + 68, x^41 + 76*x^39 + 16*x^38 + 46*x^37 + 32*x^36 + 12*x^35 + 80*x^34 + 29*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 46*x^5 + 32*x^4 + 108*x^3 + 80*x^2 + 49*x, x^41 + 76*x^39 + 68*x^38 + 70*x^37 + 124*x^36 + 92*x^35 + 92*x^34 + 117*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 6*x^5 + 92*x^4 + 60*x^3 + 124*x^2 + 73*x + 68, x^41 + 76*x^39 + 56*x^38 + 46*x^37 + 120*x^36 + 12*x^35 + 40*x^34 + 29*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 46*x^5 + 56*x^4 + 108*x^3 + 104*x^2 + 49*x + 104, x^41 + 76*x^39 + 80*x^38 + 94*x^37 + 112*x^36 + 108*x^35 + 112*x^34 + 13*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 94*x^5 + 112*x^4 + 76*x^3 + 112*x^2 + 33*x + 80, x^41 + 76*x^39 + 120*x^38 + 110*x^37 + 88*x^36 + 12*x^35 + 40*x^34 + 93*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 110*x^5 + 24*x^4 + 108*x^3 + 104*x^2 + 113*x + 72, x^41 + 76*x^39 + 68*x^38 + 70*x^37 + 92*x^36 + 92*x^35 + 28*x^34 + 117*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 6*x^5 + 60*x^4 + 60*x^3 + 60*x^2 + 73*x + 36, x^41 + 76*x^39 + 16*x^38 + 126*x^37 + 16*x^36 + 44*x^35 + 112*x^34 + 45*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 126*x^5 + 16*x^4 + 12*x^3 + 112*x^2 + 65*x + 112, x^41 + 76*x^39 + 24*x^38 + 78*x^37 + 88*x^36 + 76*x^35 + 72*x^34 + 61*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 78*x^5 + 24*x^4 + 44*x^3 + 8*x^2 + 81*x + 8, x^41 + 76*x^39 + 116*x^38 + 54*x^37 + 28*x^36 + 124*x^35 + 76*x^34 + 101*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 118*x^5 + 124*x^4 + 92*x^3 + 108*x^2 + 57*x + 4, x^41 + 76*x^39 + 100*x^38 + 70*x^37 + 92*x^36 + 92*x^35 + 60*x^34 + 117*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 6*x^5 + 60*x^4 + 60*x^3 + 92*x^2 + 73*x + 100, x^41 + 76*x^39 + 126*x^37 + 108*x^35 + 109*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 126*x^5 + 76*x^3 + x, x^41 + 76*x^39 + 12*x^38 + 70*x^37 + 20*x^36 + 92*x^35 + 20*x^34 + 117*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 6*x^5 + 52*x^4 + 60*x^3 + 116*x^2 + 73*x + 108, x^41 + 76*x^39 + 112*x^38 + 94*x^37 + 16*x^36 + 44*x^35 + 16*x^34 + 77*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 94*x^5 + 16*x^4 + 12*x^3 + 16*x^2 + 97*x + 112, x^41 + 76*x^39 + 120*x^38 + 110*x^37 + 56*x^36 + 12*x^35 + 104*x^34 + 93*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 110*x^5 + 120*x^4 + 108*x^3 + 40*x^2 + 113*x + 40, x^41 + 76*x^39 + 72*x^38 + 14*x^37 + 40*x^36 + 76*x^35 + 24*x^34 + 125*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 14*x^5 + 104*x^4 + 44*x^3 + 88*x^2 + 17*x + 56, x^41 + 76*x^39 + 24*x^38 + 14*x^37 + 120*x^36 + 76*x^35 + 8*x^34 + 125*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 14*x^5 + 56*x^4 + 44*x^3 + 72*x^2 + 17*x + 40, x^41 + 76*x^39 + 76*x^38 + 86*x^37 + 68*x^36 + 60*x^35 + 52*x^34 + 5*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 22*x^5 + 100*x^4 + 28*x^3 + 20*x^2 + 89*x + 92, x^41 + 76*x^39 + 44*x^38 + 86*x^37 + 36*x^36 + 124*x^35 + 20*x^34 + 69*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 22*x^5 + 68*x^4 + 92*x^3 + 116*x^2 + 25*x + 60, x^41 + 76*x^39 + 48*x^38 + 62*x^37 + 48*x^36 + 44*x^35 + 80*x^34 + 109*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 62*x^5 + 48*x^4 + 12*x^3 + 80*x^2 + x + 80, x^41 + 76*x^39 + 88*x^38 + 62*x^37 + 40*x^36 + 108*x^35 + 40*x^34 + 45*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 62*x^5 + 104*x^4 + 76*x^3 + 104*x^2 + 65*x + 24, x^41 + 76*x^39 + 48*x^38 + 46*x^37 + 64*x^36 + 12*x^35 + 48*x^34 + 29*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 46*x^5 + 64*x^4 + 108*x^3 + 48*x^2 + 49*x + 96, x^41 + 76*x^39 + 120*x^38 + 78*x^37 + 56*x^36 + 12*x^35 + 40*x^34 + 125*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 78*x^5 + 120*x^4 + 108*x^3 + 104*x^2 + 17*x + 104, x^41 + 76*x^39 + 52*x^38 + 86*x^37 + 124*x^36 + 60*x^35 + 76*x^34 + 5*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 22*x^5 + 92*x^4 + 28*x^3 + 108*x^2 + 89*x + 100, x^41 + 76*x^39 + 20*x^38 + 86*x^37 + 28*x^36 + 60*x^35 + 108*x^34 + 5*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 22*x^5 + 124*x^4 + 28*x^3 + 12*x^2 + 89*x + 68, x^41 + 76*x^39 + 116*x^38 + 6*x^37 + 108*x^36 + 92*x^35 + 108*x^34 + 53*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 70*x^5 + 76*x^4 + 60*x^3 + 12*x^2 + 9*x + 20, x^41 + 76*x^39 + 78*x^37 + 16*x^36 + 76*x^35 + 32*x^34 + 61*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 78*x^5 + 16*x^4 + 44*x^3 + 32*x^2 + 81*x + 80, x^41 + 76*x^39 + 88*x^38 + 126*x^37 + 8*x^36 + 44*x^35 + 40*x^34 + 45*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 126*x^5 + 72*x^4 + 12*x^3 + 104*x^2 + 65*x + 56, x^41 + 76*x^39 + 60*x^38 + 22*x^37 + 20*x^36 + 124*x^35 + 4*x^34 + 5*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 86*x^5 + 52*x^4 + 92*x^3 + 100*x^2 + 89*x + 76, x^41 + 76*x^39 + 52*x^38 + 70*x^37 + 108*x^36 + 92*x^35 + 44*x^34 + 117*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 6*x^5 + 76*x^4 + 60*x^3 + 76*x^2 + 73*x + 20, x^41 + 76*x^39 + 116*x^38 + 22*x^37 + 124*x^36 + 60*x^35 + 12*x^34 + 69*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 86*x^5 + 92*x^4 + 28*x^3 + 44*x^2 + 25*x + 100, x^41 + 76*x^39 + 52*x^38 + 6*x^37 + 108*x^36 + 92*x^35 + 44*x^34 + 53*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 70*x^5 + 76*x^4 + 60*x^3 + 76*x^2 + 9*x + 20, x^41 + 76*x^39 + 20*x^38 + 70*x^37 + 12*x^36 + 92*x^35 + 76*x^34 + 117*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 6*x^5 + 108*x^4 + 60*x^3 + 108*x^2 + 73*x + 116, x^41 + 76*x^39 + 48*x^38 + 14*x^37 + 96*x^36 + 12*x^35 + 48*x^34 + 61*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 14*x^5 + 96*x^4 + 108*x^3 + 48*x^2 + 81*x + 64, x^41 + 76*x^39 + 60*x^38 + 118*x^37 + 84*x^36 + 60*x^35 + 4*x^34 + 101*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 54*x^5 + 116*x^4 + 28*x^3 + 100*x^2 + 57*x + 12, x^41 + 76*x^39 + 108*x^38 + 54*x^37 + 4*x^36 + 124*x^35 + 84*x^34 + 101*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 118*x^5 + 36*x^4 + 92*x^3 + 52*x^2 + 57*x + 92, x^41 + 76*x^39 + 64*x^38 + 62*x^37 + 44*x^35 + 109*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 62*x^5 + 12*x^3 + x + 64, x^41 + 76*x^39 + 64*x^38 + 94*x^37 + 32*x^36 + 108*x^35 + 64*x^34 + 13*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 94*x^5 + 32*x^4 + 76*x^3 + 64*x^2 + 33*x + 96, x^41 + 76*x^39 + 120*x^38 + 62*x^37 + 40*x^36 + 44*x^35 + 8*x^34 + 109*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 62*x^5 + 104*x^4 + 12*x^3 + 72*x^2 + x + 24, x^41 + 76*x^39 + 8*x^38 + 78*x^37 + 104*x^36 + 76*x^35 + 88*x^34 + 61*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 78*x^5 + 40*x^4 + 44*x^3 + 24*x^2 + 81*x + 120, x^41 + 76*x^39 + 8*x^38 + 14*x^37 + 8*x^36 + 76*x^35 + 24*x^34 + 125*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 14*x^5 + 72*x^4 + 44*x^3 + 88*x^2 + 17*x + 24, x^41 + 76*x^39 + 112*x^38 + 78*x^37 + 96*x^36 + 76*x^35 + 48*x^34 + 61*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 78*x^5 + 96*x^4 + 44*x^3 + 48*x^2 + 81*x, x^41 + 76*x^39 + 110*x^37 + 48*x^36 + 76*x^35 + 32*x^34 + 29*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 110*x^5 + 48*x^4 + 44*x^3 + 32*x^2 + 49*x + 48, x^41 + 76*x^39 + 24*x^38 + 30*x^37 + 8*x^36 + 44*x^35 + 40*x^34 + 13*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 30*x^5 + 72*x^4 + 12*x^3 + 104*x^2 + 33*x + 120, x^41 + 76*x^39 + 108*x^38 + 6*x^37 + 20*x^36 + 92*x^35 + 116*x^34 + 53*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 70*x^5 + 52*x^4 + 60*x^3 + 84*x^2 + 9*x + 44, x^41 + 76*x^39 + 36*x^38 + 102*x^37 + 60*x^36 + 92*x^35 + 124*x^34 + 85*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 38*x^5 + 28*x^4 + 60*x^3 + 28*x^2 + 41*x + 4, x^41 + 76*x^39 + 100*x^38 + 38*x^37 + 28*x^36 + 28*x^35 + 60*x^34 + 85*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 102*x^5 + 124*x^4 + 124*x^3 + 92*x^2 + 41*x + 36, x^41 + 76*x^39 + 16*x^38 + 126*x^37 + 112*x^36 + 108*x^35 + 112*x^34 + 109*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 126*x^5 + 112*x^4 + 76*x^3 + 112*x^2 + x + 16, x^41 + 76*x^39 + 16*x^38 + 14*x^37 + 64*x^36 + 12*x^35 + 80*x^34 + 61*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 14*x^5 + 64*x^4 + 108*x^3 + 80*x^2 + 81*x + 96, x^41 + 76*x^39 + 84*x^38 + 38*x^37 + 108*x^36 + 92*x^35 + 12*x^34 + 21*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 102*x^5 + 76*x^4 + 60*x^3 + 44*x^2 + 105*x + 20, x^41 + 76*x^39 + 56*x^38 + 94*x^37 + 72*x^36 + 44*x^35 + 72*x^34 + 77*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 94*x^5 + 8*x^4 + 12*x^3 + 8*x^2 + 97*x + 120, x^41 + 76*x^39 + 52*x^38 + 86*x^37 + 28*x^36 + 60*x^35 + 12*x^34 + 5*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 22*x^5 + 124*x^4 + 28*x^3 + 44*x^2 + 89*x + 4, x^41 + 76*x^39 + 84*x^38 + 86*x^37 + 60*x^36 + 124*x^35 + 44*x^34 + 69*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 22*x^5 + 28*x^4 + 92*x^3 + 76*x^2 + 25*x + 36, x^41 + 76*x^39 + 12*x^38 + 22*x^37 + 100*x^36 + 60*x^35 + 52*x^34 + 69*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 86*x^5 + 4*x^4 + 28*x^3 + 20*x^2 + 25*x + 124, x^41 + 76*x^39 + 108*x^38 + 86*x^37 + 100*x^36 + 124*x^35 + 84*x^34 + 69*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 22*x^5 + 4*x^4 + 92*x^3 + 52*x^2 + 25*x + 124, x^41 + 76*x^39 + 44*x^38 + 118*x^37 + 36*x^36 + 124*x^35 + 84*x^34 + 37*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 54*x^5 + 68*x^4 + 92*x^3 + 52*x^2 + 121*x + 124, x^41 + 76*x^39 + 48*x^38 + 78*x^37 + 64*x^36 + 12*x^35 + 112*x^34 + 125*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 78*x^5 + 64*x^4 + 108*x^3 + 112*x^2 + 17*x + 32, x^41 + 76*x^39 + 80*x^38 + 110*x^37 + 76*x^35 + 16*x^34 + 29*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 110*x^5 + 44*x^3 + 16*x^2 + 49*x + 32, x^41 + 76*x^39 + 92*x^38 + 6*x^37 + 36*x^36 + 28*x^35 + 68*x^34 + 117*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 70*x^5 + 68*x^4 + 124*x^3 + 36*x^2 + 73*x + 92, x^41 + 76*x^39 + 28*x^38 + 38*x^37 + 36*x^36 + 28*x^35 + 68*x^34 + 85*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 102*x^5 + 68*x^4 + 124*x^3 + 36*x^2 + 41*x + 28, x^41 + 76*x^39 + 36*x^38 + 22*x^37 + 108*x^36 + 60*x^35 + 28*x^34 + 69*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 86*x^5 + 76*x^4 + 28*x^3 + 60*x^2 + 25*x + 52, x^41 + 76*x^39 + 32*x^38 + 94*x^37 + 64*x^36 + 108*x^35 + 96*x^34 + 13*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 94*x^5 + 64*x^4 + 76*x^3 + 96*x^2 + 33*x + 64, x^41 + 76*x^39 + 78*x^37 + 80*x^36 + 76*x^35 + 32*x^34 + 61*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 78*x^5 + 80*x^4 + 44*x^3 + 32*x^2 + 81*x + 16, x^41 + 76*x^39 + 60*x^38 + 118*x^37 + 84*x^36 + 124*x^35 + 68*x^34 + 37*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 54*x^5 + 116*x^4 + 92*x^3 + 36*x^2 + 121*x + 76, x^41 + 76*x^39 + 100*x^38 + 22*x^37 + 108*x^36 + 124*x^35 + 28*x^34 + 5*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 86*x^5 + 76*x^4 + 92*x^3 + 60*x^2 + 89*x + 116, x^41 + 76*x^39 + 36*x^38 + 38*x^37 + 92*x^36 + 92*x^35 + 60*x^34 + 21*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 102*x^5 + 60*x^4 + 60*x^3 + 92*x^2 + 105*x + 36, x^41 + 76*x^39 + 52*x^38 + 6*x^37 + 12*x^36 + 92*x^35 + 108*x^34 + 53*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 70*x^5 + 108*x^4 + 60*x^3 + 12*x^2 + 9*x + 52, x^41 + 76*x^39 + 44*x^38 + 70*x^37 + 84*x^36 + 92*x^35 + 52*x^34 + 117*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 6*x^5 + 116*x^4 + 60*x^3 + 20*x^2 + 73*x + 108, x^41 + 76*x^39 + 28*x^38 + 6*x^37 + 100*x^36 + 28*x^35 + 4*x^34 + 117*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 70*x^5 + 4*x^4 + 124*x^3 + 100*x^2 + 73*x + 28, x^41 + 76*x^39 + 28*x^38 + 70*x^37 + 100*x^36 + 28*x^35 + 4*x^34 + 53*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 6*x^5 + 4*x^4 + 124*x^3 + 100*x^2 + 9*x + 28, x^41 + 76*x^39 + 76*x^38 + 86*x^37 + 68*x^36 + 124*x^35 + 116*x^34 + 69*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 22*x^5 + 100*x^4 + 92*x^3 + 84*x^2 + 25*x + 28, x^41 + 76*x^39 + 120*x^38 + 78*x^37 + 120*x^36 + 76*x^35 + 104*x^34 + 61*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 78*x^5 + 56*x^4 + 44*x^3 + 40*x^2 + 81*x + 104, x^41 + 76*x^39 + 100*x^38 + 70*x^37 + 124*x^36 + 92*x^35 + 124*x^34 + 117*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 6*x^5 + 92*x^4 + 60*x^3 + 28*x^2 + 73*x + 4, x^41 + 76*x^39 + 4*x^38 + 38*x^37 + 28*x^36 + 92*x^35 + 28*x^34 + 21*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 102*x^5 + 124*x^4 + 60*x^3 + 60*x^2 + 105*x + 36, x^41 + 76*x^39 + 124*x^38 + 86*x^37 + 116*x^36 + 60*x^35 + 68*x^34 + 5*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 22*x^5 + 20*x^4 + 28*x^3 + 36*x^2 + 89*x + 108, x^41 + 76*x^39 + 104*x^38 + 30*x^37 + 56*x^36 + 108*x^35 + 24*x^34 + 77*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 30*x^5 + 120*x^4 + 76*x^3 + 88*x^2 + 97*x + 8, x^41 + 76*x^39 + 126*x^37 + 96*x^36 + 44*x^35 + 45*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 64*x^20 + 40*x^19 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 126*x^5 + 96*x^4 + 12*x^3 + 65*x + 32, x^41 + 76*x^39 + 108*x^38 + 38*x^37 + 84*x^36 + 28*x^35 + 116*x^34 + 85*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 102*x^5 + 116*x^4 + 124*x^3 + 84*x^2 + 41*x + 108, x^41 + 76*x^39 + 24*x^38 + 14*x^37 + 24*x^36 + 76*x^35 + 72*x^34 + 125*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 14*x^5 + 88*x^4 + 44*x^3 + 8*x^2 + 17*x + 72, x^41 + 76*x^39 + 8*x^38 + 62*x^37 + 24*x^36 + 44*x^35 + 120*x^34 + 109*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 62*x^5 + 88*x^4 + 12*x^3 + 56*x^2 + x + 40, x^41 + 76*x^39 + 40*x^38 + 62*x^37 + 120*x^36 + 44*x^35 + 88*x^34 + 109*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 62*x^5 + 56*x^4 + 12*x^3 + 24*x^2 + x + 72, x^41 + 76*x^39 + 124*x^38 + 86*x^37 + 52*x^36 + 124*x^35 + 4*x^34 + 69*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 22*x^5 + 84*x^4 + 92*x^3 + 100*x^2 + 25*x + 108, x^41 + 76*x^39 + 36*x^38 + 22*x^37 + 76*x^36 + 60*x^35 + 92*x^34 + 69*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 86*x^5 + 44*x^4 + 28*x^3 + 124*x^2 + 25*x + 20, x^41 + 76*x^39 + 96*x^38 + 30*x^37 + 32*x^36 + 44*x^35 + 32*x^34 + 13*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 30*x^5 + 32*x^4 + 12*x^3 + 32*x^2 + 33*x + 96, x^41 + 76*x^39 + 72*x^38 + 94*x^37 + 24*x^36 + 108*x^35 + 56*x^34 + 13*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 94*x^5 + 88*x^4 + 76*x^3 + 120*x^2 + 33*x + 40, x^41 + 76*x^39 + 12*x^38 + 22*x^37 + 100*x^36 + 124*x^35 + 116*x^34 + 5*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 86*x^5 + 4*x^4 + 92*x^3 + 84*x^2 + 89*x + 60, x^41 + 76*x^39 + 60*x^38 + 38*x^37 + 36*x^36 + 92*x^35 + 36*x^34 + 21*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 102*x^5 + 68*x^4 + 60*x^3 + 4*x^2 + 105*x + 28, x^41 + 76*x^39 + 40*x^38 + 14*x^37 + 40*x^36 + 12*x^35 + 56*x^34 + 61*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 14*x^5 + 104*x^4 + 108*x^3 + 120*x^2 + 81*x + 56, x^41 + 76*x^39 + 84*x^38 + 70*x^37 + 108*x^36 + 28*x^35 + 12*x^34 + 53*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 6*x^5 + 76*x^4 + 124*x^3 + 44*x^2 + 9*x + 20, x^41 + 76*x^39 + 104*x^38 + 46*x^37 + 8*x^36 + 12*x^35 + 120*x^34 + 29*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 46*x^5 + 72*x^4 + 108*x^3 + 56*x^2 + 49*x + 88, x^41 + 76*x^39 + 96*x^38 + 78*x^37 + 48*x^36 + 76*x^35 + 64*x^34 + 61*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 78*x^5 + 48*x^4 + 44*x^3 + 64*x^2 + 81*x + 48, x^41 + 76*x^39 + 108*x^38 + 6*x^37 + 52*x^36 + 92*x^35 + 52*x^34 + 53*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 70*x^5 + 84*x^4 + 60*x^3 + 20*x^2 + 9*x + 76, x^41 + 76*x^39 + 36*x^38 + 22*x^37 + 44*x^36 + 124*x^35 + 92*x^34 + 5*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 86*x^5 + 12*x^4 + 92*x^3 + 124*x^2 + 89*x + 52, x^41 + 76*x^39 + 72*x^38 + 46*x^37 + 8*x^36 + 12*x^35 + 88*x^34 + 29*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 46*x^5 + 72*x^4 + 108*x^3 + 24*x^2 + 49*x + 24, x^41 + 76*x^39 + 20*x^38 + 102*x^37 + 44*x^36 + 92*x^35 + 76*x^34 + 85*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 38*x^5 + 12*x^4 + 60*x^3 + 108*x^2 + 41*x + 84, x^41 + 76*x^39 + 92*x^38 + 22*x^37 + 20*x^36 + 124*x^35 + 36*x^34 + 5*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 86*x^5 + 52*x^4 + 92*x^3 + 4*x^2 + 89*x + 12, x^41 + 76*x^39 + 56*x^38 + 46*x^37 + 56*x^36 + 12*x^35 + 40*x^34 + 29*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 46*x^5 + 120*x^4 + 108*x^3 + 104*x^2 + 49*x + 40, x^41 + 76*x^39 + 28*x^38 + 86*x^37 + 84*x^36 + 124*x^35 + 100*x^34 + 69*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 22*x^5 + 116*x^4 + 92*x^3 + 68*x^2 + 25*x + 76, x^41 + 76*x^39 + 72*x^38 + 110*x^37 + 8*x^36 + 76*x^35 + 24*x^34 + 29*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 110*x^5 + 72*x^4 + 44*x^3 + 88*x^2 + 49*x + 88, x^41 + 76*x^39 + 96*x^38 + 126*x^37 + 96*x^36 + 108*x^35 + 32*x^34 + 109*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 126*x^5 + 96*x^4 + 76*x^3 + 32*x^2 + x + 32, x^41 + 76*x^39 + 4*x^38 + 118*x^37 + 12*x^36 + 124*x^35 + 60*x^34 + 37*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 54*x^5 + 108*x^4 + 92*x^3 + 92*x^2 + 121*x + 20, x^41 + 76*x^39 + 80*x^38 + 78*x^37 + 12*x^35 + 16*x^34 + 125*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 78*x^5 + 108*x^3 + 16*x^2 + 17*x + 32, x^41 + 76*x^39 + 100*x^38 + 6*x^37 + 124*x^36 + 92*x^35 + 124*x^34 + 53*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 70*x^5 + 92*x^4 + 60*x^3 + 28*x^2 + 9*x + 4, x^41 + 76*x^39 + 120*x^38 + 62*x^37 + 104*x^36 + 44*x^35 + 8*x^34 + 109*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 62*x^5 + 40*x^4 + 12*x^3 + 72*x^2 + x + 88, x^41 + 76*x^39 + 80*x^38 + 110*x^37 + 96*x^36 + 76*x^35 + 80*x^34 + 29*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 110*x^5 + 96*x^4 + 44*x^3 + 80*x^2 + 49*x, x^41 + 76*x^39 + 36*x^38 + 102*x^37 + 28*x^36 + 28*x^35 + 124*x^34 + 21*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 38*x^5 + 124*x^4 + 124*x^3 + 28*x^2 + 105*x + 36, x^41 + 76*x^39 + 108*x^38 + 102*x^37 + 84*x^36 + 92*x^35 + 52*x^34 + 85*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 38*x^5 + 116*x^4 + 60*x^3 + 20*x^2 + 41*x + 44, x^41 + 76*x^39 + 68*x^38 + 86*x^37 + 76*x^36 + 60*x^35 + 124*x^34 + 5*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 22*x^5 + 44*x^4 + 28*x^3 + 28*x^2 + 89*x + 84, x^41 + 76*x^39 + 40*x^38 + 110*x^37 + 72*x^36 + 12*x^35 + 56*x^34 + 93*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 110*x^5 + 8*x^4 + 108*x^3 + 120*x^2 + 113*x + 24, x^41 + 76*x^39 + 104*x^38 + 30*x^37 + 88*x^36 + 108*x^35 + 88*x^34 + 77*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 30*x^5 + 24*x^4 + 76*x^3 + 24*x^2 + 97*x + 40, x^41 + 76*x^39 + 44*x^38 + 38*x^37 + 84*x^36 + 92*x^35 + 116*x^34 + 21*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 102*x^5 + 116*x^4 + 60*x^3 + 84*x^2 + 105*x + 44, x^41 + 76*x^39 + 28*x^38 + 38*x^37 + 68*x^36 + 28*x^35 + 4*x^34 + 85*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 102*x^5 + 100*x^4 + 124*x^3 + 100*x^2 + 41*x + 60, x^41 + 76*x^39 + 52*x^38 + 22*x^37 + 92*x^36 + 124*x^35 + 76*x^34 + 5*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 86*x^5 + 60*x^4 + 92*x^3 + 108*x^2 + 89*x + 4, x^41 + 76*x^39 + 16*x^38 + 126*x^37 + 112*x^36 + 44*x^35 + 48*x^34 + 45*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 126*x^5 + 112*x^4 + 12*x^3 + 48*x^2 + 65*x + 80, x^41 + 76*x^39 + 84*x^38 + 54*x^37 + 60*x^36 + 60*x^35 + 44*x^34 + 37*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 118*x^5 + 28*x^4 + 28*x^3 + 76*x^2 + 121*x + 36, x^41 + 76*x^39 + 8*x^38 + 110*x^37 + 104*x^36 + 12*x^35 + 88*x^34 + 93*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 110*x^5 + 40*x^4 + 108*x^3 + 24*x^2 + 113*x + 120, x^41 + 76*x^39 + 52*x^38 + 86*x^37 + 60*x^36 + 124*x^35 + 12*x^34 + 69*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 22*x^5 + 28*x^4 + 92*x^3 + 44*x^2 + 25*x + 100, x^41 + 76*x^39 + 72*x^38 + 94*x^37 + 120*x^36 + 108*x^35 + 120*x^34 + 13*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 94*x^5 + 56*x^4 + 76*x^3 + 56*x^2 + 33*x + 8, x^41 + 76*x^39 + 32*x^38 + 14*x^37 + 80*x^36 + 76*x^35 + 64*x^34 + 125*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 14*x^5 + 80*x^4 + 44*x^3 + 64*x^2 + 17*x + 80, x^41 + 76*x^39 + 32*x^38 + 46*x^37 + 112*x^36 + 76*x^35 + 64*x^34 + 93*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 46*x^5 + 112*x^4 + 44*x^3 + 64*x^2 + 113*x + 48, x^41 + 76*x^39 + 16*x^38 + 94*x^37 + 80*x^36 + 44*x^35 + 48*x^34 + 77*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 94*x^5 + 80*x^4 + 12*x^3 + 48*x^2 + 97*x + 112, x^41 + 76*x^39 + 48*x^38 + 14*x^37 + 32*x^36 + 76*x^35 + 112*x^34 + 125*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 14*x^5 + 32*x^4 + 44*x^3 + 112*x^2 + 17*x + 64, x^41 + 76*x^39 + 76*x^38 + 70*x^37 + 52*x^36 + 92*x^35 + 20*x^34 + 117*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 6*x^5 + 84*x^4 + 60*x^3 + 116*x^2 + 73*x + 12, x^41 + 76*x^39 + 108*x^38 + 118*x^37 + 4*x^36 + 60*x^35 + 20*x^34 + 101*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 54*x^5 + 36*x^4 + 28*x^3 + 116*x^2 + 57*x + 28, x^41 + 76*x^39 + 36*x^38 + 86*x^37 + 108*x^36 + 60*x^35 + 28*x^34 + 5*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 22*x^5 + 76*x^4 + 28*x^3 + 60*x^2 + 89*x + 52, x^41 + 76*x^39 + 24*x^38 + 110*x^37 + 120*x^36 + 76*x^35 + 72*x^34 + 29*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 110*x^5 + 56*x^4 + 44*x^3 + 8*x^2 + 49*x + 104, x^41 + 76*x^39 + 40*x^38 + 126*x^37 + 88*x^36 + 44*x^35 + 24*x^34 + 45*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 126*x^5 + 24*x^4 + 12*x^3 + 88*x^2 + 65*x + 40, x^41 + 76*x^39 + 108*x^38 + 70*x^37 + 20*x^36 + 28*x^35 + 52*x^34 + 53*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 6*x^5 + 52*x^4 + 124*x^3 + 20*x^2 + 9*x + 108, x^41 + 76*x^39 + 124*x^38 + 38*x^37 + 36*x^36 + 92*x^35 + 100*x^34 + 21*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 102*x^5 + 68*x^4 + 60*x^3 + 68*x^2 + 105*x + 28, x^41 + 76*x^39 + 4*x^38 + 6*x^37 + 92*x^36 + 28*x^35 + 28*x^34 + 117*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 70*x^5 + 60*x^4 + 124*x^3 + 60*x^2 + 73*x + 100, x^41 + 76*x^39 + 104*x^38 + 14*x^37 + 104*x^36 + 76*x^35 + 56*x^34 + 125*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 14*x^5 + 40*x^4 + 44*x^3 + 120*x^2 + 17*x + 56, x^41 + 76*x^39 + 88*x^38 + 30*x^37 + 72*x^36 + 108*x^35 + 40*x^34 + 77*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 30*x^5 + 8*x^4 + 76*x^3 + 104*x^2 + 97*x + 120, x^41 + 76*x^39 + 52*x^38 + 86*x^37 + 92*x^36 + 60*x^35 + 12*x^34 + 5*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 22*x^5 + 60*x^4 + 28*x^3 + 44*x^2 + 89*x + 68, x^41 + 76*x^39 + 64*x^38 + 110*x^37 + 80*x^36 + 76*x^35 + 32*x^34 + 29*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 110*x^5 + 80*x^4 + 44*x^3 + 32*x^2 + 49*x + 80, x^41 + 76*x^39 + 24*x^38 + 62*x^37 + 8*x^36 + 108*x^35 + 40*x^34 + 45*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 62*x^5 + 72*x^4 + 76*x^3 + 104*x^2 + 65*x + 120, x^41 + 76*x^39 + 60*x^38 + 54*x^37 + 116*x^36 + 60*x^35 + 68*x^34 + 37*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 118*x^5 + 20*x^4 + 28*x^3 + 36*x^2 + 121*x + 44, x^41 + 76*x^39 + 76*x^38 + 102*x^37 + 116*x^36 + 28*x^35 + 20*x^34 + 21*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 38*x^5 + 20*x^4 + 124*x^3 + 116*x^2 + 105*x + 76, x^41 + 76*x^39 + 36*x^38 + 54*x^37 + 76*x^36 + 124*x^35 + 92*x^34 + 101*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 118*x^5 + 44*x^4 + 92*x^3 + 124*x^2 + 57*x + 20, x^41 + 76*x^39 + 32*x^38 + 78*x^37 + 48*x^36 + 76*x^35 + 61*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 78*x^5 + 48*x^4 + 44*x^3 + 81*x + 48, x^41 + 76*x^39 + 4*x^38 + 118*x^37 + 76*x^36 + 60*x^35 + 124*x^34 + 101*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 54*x^5 + 44*x^4 + 28*x^3 + 28*x^2 + 57*x + 20, x^41 + 76*x^39 + 32*x^38 + 94*x^37 + 32*x^36 + 108*x^35 + 32*x^34 + 13*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 94*x^5 + 32*x^4 + 76*x^3 + 32*x^2 + 33*x + 32, x^41 + 76*x^39 + 32*x^38 + 62*x^37 + 32*x^36 + 44*x^35 + 32*x^34 + 109*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 62*x^5 + 32*x^4 + 12*x^3 + 32*x^2 + x + 32, x^41 + 76*x^39 + 44*x^38 + 38*x^37 + 116*x^36 + 28*x^35 + 116*x^34 + 85*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 102*x^5 + 20*x^4 + 124*x^3 + 84*x^2 + 41*x + 12, x^41 + 76*x^39 + 104*x^38 + 126*x^37 + 56*x^36 + 108*x^35 + 88*x^34 + 109*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 126*x^5 + 120*x^4 + 76*x^3 + 24*x^2 + x + 72, x^41 + 76*x^39 + 112*x^38 + 126*x^37 + 112*x^36 + 44*x^35 + 16*x^34 + 45*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 126*x^5 + 112*x^4 + 12*x^3 + 16*x^2 + 65*x + 16, x^41 + 76*x^39 + 64*x^38 + 14*x^37 + 48*x^36 + 12*x^35 + 96*x^34 + 61*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 14*x^5 + 48*x^4 + 108*x^3 + 96*x^2 + 81*x + 48, x^41 + 76*x^39 + 96*x^38 + 94*x^37 + 64*x^36 + 108*x^35 + 32*x^34 + 13*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 94*x^5 + 64*x^4 + 76*x^3 + 32*x^2 + 33*x + 64, x^41 + 76*x^39 + 24*x^38 + 78*x^37 + 120*x^36 + 12*x^35 + 72*x^34 + 125*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 78*x^5 + 56*x^4 + 108*x^3 + 8*x^2 + 17*x + 104, x^41 + 76*x^39 + 28*x^38 + 86*x^37 + 20*x^36 + 60*x^35 + 36*x^34 + 5*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 22*x^5 + 52*x^4 + 28*x^3 + 4*x^2 + 89*x + 76, x^41 + 76*x^39 + 4*x^38 + 54*x^37 + 76*x^36 + 60*x^35 + 124*x^34 + 37*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 118*x^5 + 44*x^4 + 28*x^3 + 28*x^2 + 121*x + 20, x^41 + 76*x^39 + 76*x^38 + 6*x^37 + 52*x^36 + 92*x^35 + 20*x^34 + 53*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 70*x^5 + 84*x^4 + 60*x^3 + 116*x^2 + 9*x + 12, x^41 + 76*x^39 + 16*x^38 + 46*x^37 + 96*x^36 + 76*x^35 + 16*x^34 + 93*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 46*x^5 + 96*x^4 + 44*x^3 + 16*x^2 + 113*x, x^41 + 76*x^39 + 116*x^38 + 6*x^37 + 44*x^36 + 92*x^35 + 108*x^34 + 53*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 70*x^5 + 12*x^4 + 60*x^3 + 12*x^2 + 9*x + 84, x^41 + 76*x^39 + 4*x^38 + 54*x^37 + 108*x^36 + 124*x^35 + 124*x^34 + 101*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 118*x^5 + 76*x^4 + 92*x^3 + 28*x^2 + 57*x + 116, x^41 + 76*x^39 + 100*x^38 + 118*x^37 + 44*x^36 + 60*x^35 + 28*x^34 + 101*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 54*x^5 + 12*x^4 + 28*x^3 + 60*x^2 + 57*x + 52, x^41 + 76*x^39 + 124*x^38 + 38*x^37 + 4*x^36 + 28*x^35 + 100*x^34 + 85*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 102*x^5 + 36*x^4 + 124*x^3 + 68*x^2 + 41*x + 60, x^41 + 76*x^39 + 76*x^38 + 38*x^37 + 116*x^36 + 28*x^35 + 20*x^34 + 85*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 102*x^5 + 20*x^4 + 124*x^3 + 116*x^2 + 41*x + 76, x^41 + 76*x^39 + 56*x^38 + 30*x^37 + 40*x^36 + 108*x^35 + 72*x^34 + 77*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 30*x^5 + 104*x^4 + 76*x^3 + 8*x^2 + 97*x + 24, x^41 + 76*x^39 + 12*x^38 + 38*x^37 + 52*x^36 + 92*x^35 + 20*x^34 + 21*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 102*x^5 + 84*x^4 + 60*x^3 + 116*x^2 + 105*x + 76, x^41 + 76*x^39 + 92*x^38 + 70*x^37 + 36*x^36 + 92*x^35 + 4*x^34 + 117*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 6*x^5 + 68*x^4 + 60*x^3 + 100*x^2 + 73*x + 28, x^41 + 76*x^39 + 124*x^38 + 54*x^37 + 84*x^36 + 60*x^35 + 68*x^34 + 37*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 118*x^5 + 116*x^4 + 28*x^3 + 36*x^2 + 121*x + 12, x^41 + 76*x^39 + 24*x^38 + 126*x^37 + 104*x^36 + 44*x^35 + 40*x^34 + 45*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 126*x^5 + 40*x^4 + 12*x^3 + 104*x^2 + 65*x + 24, x^41 + 76*x^39 + 4*x^38 + 6*x^37 + 124*x^36 + 28*x^35 + 92*x^34 + 117*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 70*x^5 + 92*x^4 + 124*x^3 + 124*x^2 + 73*x + 4, x^41 + 76*x^39 + 88*x^38 + 30*x^37 + 8*x^36 + 44*x^35 + 104*x^34 + 13*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 30*x^5 + 72*x^4 + 12*x^3 + 40*x^2 + 33*x + 120, x^41 + 76*x^39 + 4*x^38 + 70*x^37 + 124*x^36 + 28*x^35 + 92*x^34 + 53*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 6*x^5 + 92*x^4 + 124*x^3 + 124*x^2 + 9*x + 4, x^41 + 76*x^39 + 64*x^38 + 46*x^37 + 16*x^36 + 76*x^35 + 32*x^34 + 93*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 46*x^5 + 16*x^4 + 44*x^3 + 32*x^2 + 113*x + 16, x^41 + 76*x^39 + 68*x^38 + 6*x^37 + 124*x^36 + 92*x^35 + 92*x^34 + 53*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 70*x^5 + 92*x^4 + 60*x^3 + 124*x^2 + 9*x + 68, x^41 + 76*x^39 + 100*x^38 + 118*x^37 + 108*x^36 + 124*x^35 + 92*x^34 + 37*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 54*x^5 + 76*x^4 + 92*x^3 + 124*x^2 + 121*x + 52, x^41 + 76*x^39 + 20*x^38 + 102*x^37 + 76*x^36 + 92*x^35 + 12*x^34 + 85*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 38*x^5 + 44*x^4 + 60*x^3 + 44*x^2 + 41*x + 116, x^41 + 76*x^39 + 20*x^38 + 86*x^37 + 60*x^36 + 60*x^35 + 44*x^34 + 5*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 22*x^5 + 28*x^4 + 28*x^3 + 76*x^2 + 89*x + 100, x^41 + 76*x^39 + 104*x^38 + 110*x^37 + 40*x^36 + 76*x^35 + 120*x^34 + 29*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 110*x^5 + 104*x^4 + 44*x^3 + 56*x^2 + 49*x + 56, x^41 + 76*x^39 + 56*x^38 + 78*x^37 + 88*x^36 + 12*x^35 + 40*x^34 + 125*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 78*x^5 + 24*x^4 + 108*x^3 + 104*x^2 + 17*x + 8, x^41 + 76*x^39 + 60*x^38 + 86*x^37 + 116*x^36 + 124*x^35 + 68*x^34 + 69*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 22*x^5 + 20*x^4 + 92*x^3 + 36*x^2 + 25*x + 44, x^41 + 76*x^39 + 76*x^38 + 86*x^37 + 100*x^36 + 124*x^35 + 52*x^34 + 69*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 22*x^5 + 4*x^4 + 92*x^3 + 20*x^2 + 25*x + 60, x^41 + 76*x^39 + 80*x^38 + 62*x^37 + 48*x^36 + 108*x^35 + 48*x^34 + 45*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 62*x^5 + 48*x^4 + 76*x^3 + 48*x^2 + 65*x + 80, x^41 + 76*x^39 + 52*x^38 + 118*x^37 + 60*x^36 + 124*x^35 + 76*x^34 + 37*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 54*x^5 + 28*x^4 + 92*x^3 + 108*x^2 + 121*x + 36, x^41 + 76*x^39 + 12*x^38 + 102*x^37 + 84*x^36 + 92*x^35 + 84*x^34 + 85*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 38*x^5 + 116*x^4 + 60*x^3 + 52*x^2 + 41*x + 108, x^41 + 76*x^39 + 80*x^38 + 94*x^37 + 48*x^36 + 44*x^35 + 48*x^34 + 77*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 94*x^5 + 48*x^4 + 12*x^3 + 48*x^2 + 97*x + 80, x^41 + 76*x^39 + 88*x^38 + 78*x^37 + 88*x^36 + 12*x^35 + 72*x^34 + 125*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 78*x^5 + 24*x^4 + 108*x^3 + 8*x^2 + 17*x + 72, x^41 + 76*x^39 + 104*x^38 + 14*x^37 + 40*x^36 + 12*x^35 + 120*x^34 + 61*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 14*x^5 + 104*x^4 + 108*x^3 + 56*x^2 + 81*x + 56, x^41 + 76*x^39 + 104*x^38 + 62*x^37 + 88*x^36 + 44*x^35 + 88*x^34 + 109*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 62*x^5 + 24*x^4 + 12*x^3 + 24*x^2 + x + 40, x^41 + 76*x^39 + 32*x^38 + 78*x^37 + 48*x^36 + 12*x^35 + 64*x^34 + 125*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 78*x^5 + 48*x^4 + 108*x^3 + 64*x^2 + 17*x + 112, x^41 + 76*x^39 + 12*x^38 + 102*x^37 + 52*x^36 + 92*x^35 + 20*x^34 + 85*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 38*x^5 + 84*x^4 + 60*x^3 + 116*x^2 + 41*x + 76, x^41 + 76*x^39 + 68*x^38 + 38*x^37 + 124*x^36 + 28*x^35 + 92*x^34 + 85*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 102*x^5 + 92*x^4 + 124*x^3 + 124*x^2 + 41*x + 68, x^41 + 76*x^39 + 88*x^38 + 62*x^37 + 104*x^36 + 44*x^35 + 104*x^34 + 109*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 62*x^5 + 40*x^4 + 12*x^3 + 40*x^2 + x + 24, x^41 + 76*x^39 + 52*x^38 + 38*x^37 + 108*x^36 + 92*x^35 + 108*x^34 + 21*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 102*x^5 + 76*x^4 + 60*x^3 + 12*x^2 + 105*x + 84, x^41 + 76*x^39 + 68*x^38 + 38*x^37 + 92*x^36 + 28*x^35 + 28*x^34 + 85*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 102*x^5 + 60*x^4 + 124*x^3 + 60*x^2 + 41*x + 36, x^41 + 76*x^39 + 36*x^38 + 22*x^37 + 44*x^36 + 60*x^35 + 28*x^34 + 69*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 86*x^5 + 12*x^4 + 28*x^3 + 60*x^2 + 25*x + 116, x^41 + 76*x^39 + 68*x^38 + 102*x^37 + 60*x^36 + 28*x^35 + 92*x^34 + 21*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 38*x^5 + 28*x^4 + 124*x^3 + 124*x^2 + 105*x + 4, x^41 + 76*x^39 + 108*x^38 + 70*x^37 + 84*x^36 + 92*x^35 + 116*x^34 + 117*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 6*x^5 + 116*x^4 + 60*x^3 + 84*x^2 + 73*x + 108, x^41 + 76*x^39 + 28*x^38 + 102*x^37 + 36*x^36 + 28*x^35 + 68*x^34 + 21*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 38*x^5 + 68*x^4 + 124*x^3 + 36*x^2 + 105*x + 28, x^41 + 76*x^39 + 104*x^38 + 94*x^37 + 88*x^36 + 44*x^35 + 24*x^34 + 77*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 94*x^5 + 24*x^4 + 12*x^3 + 88*x^2 + 97*x + 104, x^41 + 76*x^39 + 76*x^38 + 54*x^37 + 68*x^36 + 124*x^35 + 52*x^34 + 101*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 118*x^5 + 100*x^4 + 92*x^3 + 20*x^2 + 57*x + 92, x^41 + 76*x^39 + 100*x^38 + 102*x^37 + 28*x^36 + 92*x^35 + 124*x^34 + 85*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 38*x^5 + 124*x^4 + 60*x^3 + 28*x^2 + 41*x + 100, x^41 + 76*x^39 + 88*x^38 + 78*x^37 + 56*x^36 + 76*x^35 + 72*x^34 + 61*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 78*x^5 + 120*x^4 + 44*x^3 + 8*x^2 + 81*x + 104, x^41 + 76*x^39 + 56*x^38 + 94*x^37 + 40*x^36 + 44*x^35 + 8*x^34 + 77*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 94*x^5 + 104*x^4 + 12*x^3 + 72*x^2 + 97*x + 88, x^41 + 76*x^39 + 112*x^38 + 126*x^37 + 80*x^36 + 44*x^35 + 80*x^34 + 45*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 126*x^5 + 80*x^4 + 12*x^3 + 80*x^2 + 65*x + 112, x^41 + 76*x^39 + 72*x^38 + 14*x^37 + 40*x^36 + 12*x^35 + 88*x^34 + 61*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 14*x^5 + 104*x^4 + 108*x^3 + 24*x^2 + 81*x + 120, x^41 + 76*x^39 + 8*x^38 + 30*x^37 + 24*x^36 + 44*x^35 + 56*x^34 + 13*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 30*x^5 + 88*x^4 + 12*x^3 + 120*x^2 + 33*x + 104, x^41 + 76*x^39 + 110*x^37 + 112*x^36 + 76*x^35 + 32*x^34 + 29*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 110*x^5 + 112*x^4 + 44*x^3 + 32*x^2 + 49*x + 112, x^41 + 76*x^39 + 92*x^38 + 54*x^37 + 52*x^36 + 60*x^35 + 100*x^34 + 37*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 118*x^5 + 84*x^4 + 28*x^3 + 68*x^2 + 121*x + 44, x^41 + 76*x^39 + 72*x^38 + 126*x^37 + 24*x^36 + 108*x^35 + 120*x^34 + 109*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 126*x^5 + 88*x^4 + 76*x^3 + 56*x^2 + x + 104, x^41 + 76*x^39 + 4*x^38 + 22*x^37 + 76*x^36 + 124*x^35 + 124*x^34 + 5*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 86*x^5 + 44*x^4 + 92*x^3 + 28*x^2 + 89*x + 20, x^41 + 76*x^39 + 48*x^38 + 94*x^37 + 16*x^36 + 108*x^35 + 16*x^34 + 13*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 94*x^5 + 16*x^4 + 76*x^3 + 16*x^2 + 33*x + 48, x^41 + 76*x^39 + 48*x^38 + 62*x^37 + 16*x^36 + 108*x^35 + 80*x^34 + 45*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 62*x^5 + 16*x^4 + 76*x^3 + 80*x^2 + 65*x + 112, x^41 + 76*x^39 + 28*x^38 + 6*x^37 + 100*x^36 + 92*x^35 + 68*x^34 + 53*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 70*x^5 + 4*x^4 + 60*x^3 + 36*x^2 + 9*x + 92, x^41 + 76*x^39 + 80*x^38 + 62*x^37 + 112*x^36 + 44*x^35 + 112*x^34 + 109*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 62*x^5 + 112*x^4 + 12*x^3 + 112*x^2 + x + 80, x^41 + 76*x^39 + 72*x^38 + 14*x^37 + 104*x^36 + 12*x^35 + 88*x^34 + 61*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 14*x^5 + 40*x^4 + 108*x^3 + 24*x^2 + 81*x + 56, x^41 + 76*x^39 + 64*x^38 + 62*x^37 + 64*x^36 + 108*x^35 + 64*x^34 + 45*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 62*x^5 + 64*x^4 + 76*x^3 + 64*x^2 + 65*x + 64, x^41 + 76*x^39 + 20*x^38 + 102*x^37 + 44*x^36 + 28*x^35 + 12*x^34 + 21*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 38*x^5 + 12*x^4 + 124*x^3 + 44*x^2 + 105*x + 20, x^41 + 76*x^39 + 72*x^38 + 46*x^37 + 72*x^36 + 12*x^35 + 88*x^34 + 29*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 46*x^5 + 8*x^4 + 108*x^3 + 24*x^2 + 49*x + 88, x^41 + 76*x^39 + 32*x^38 + 78*x^37 + 112*x^36 + 12*x^35 + 64*x^34 + 125*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 78*x^5 + 112*x^4 + 108*x^3 + 64*x^2 + 17*x + 48, x^41 + 76*x^39 + 52*x^38 + 38*x^37 + 108*x^36 + 28*x^35 + 44*x^34 + 85*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 102*x^5 + 76*x^4 + 124*x^3 + 76*x^2 + 41*x + 20, x^41 + 76*x^39 + 116*x^38 + 22*x^37 + 60*x^36 + 124*x^35 + 76*x^34 + 5*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 86*x^5 + 28*x^4 + 92*x^3 + 108*x^2 + 89*x + 100, x^41 + 76*x^39 + 76*x^38 + 102*x^37 + 116*x^36 + 92*x^35 + 84*x^34 + 85*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 38*x^5 + 20*x^4 + 60*x^3 + 52*x^2 + 41*x + 12, x^41 + 76*x^39 + 36*x^38 + 70*x^37 + 60*x^36 + 92*x^35 + 60*x^34 + 117*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 6*x^5 + 28*x^4 + 60*x^3 + 92*x^2 + 73*x + 68, x^41 + 76*x^39 + 36*x^38 + 6*x^37 + 60*x^36 + 92*x^35 + 60*x^34 + 53*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 70*x^5 + 28*x^4 + 60*x^3 + 92*x^2 + 9*x + 68, x^41 + 76*x^39 + 92*x^38 + 22*x^37 + 52*x^36 + 124*x^35 + 100*x^34 + 5*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 86*x^5 + 84*x^4 + 92*x^3 + 68*x^2 + 89*x + 44, x^41 + 76*x^39 + 68*x^38 + 6*x^37 + 92*x^36 + 28*x^35 + 92*x^34 + 117*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 70*x^5 + 60*x^4 + 124*x^3 + 124*x^2 + 73*x + 100, x^41 + 76*x^39 + 112*x^38 + 14*x^37 + 12*x^35 + 48*x^34 + 61*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 14*x^5 + 108*x^3 + 48*x^2 + 81*x + 96, x^41 + 76*x^39 + 112*x^38 + 14*x^37 + 96*x^36 + 12*x^35 + 112*x^34 + 61*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 14*x^5 + 96*x^4 + 108*x^3 + 112*x^2 + 81*x + 64, x^41 + 76*x^39 + 108*x^38 + 118*x^37 + 100*x^36 + 124*x^35 + 20*x^34 + 37*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 54*x^5 + 4*x^4 + 92*x^3 + 116*x^2 + 121*x + 60, x^41 + 76*x^39 + 12*x^38 + 102*x^37 + 52*x^36 + 28*x^35 + 84*x^34 + 21*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 38*x^5 + 84*x^4 + 124*x^3 + 52*x^2 + 105*x + 12, x^41 + 76*x^39 + 24*x^38 + 46*x^37 + 120*x^36 + 12*x^35 + 8*x^34 + 29*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 46*x^5 + 56*x^4 + 108*x^3 + 72*x^2 + 49*x + 40, x^41 + 76*x^39 + 124*x^38 + 70*x^37 + 100*x^36 + 28*x^35 + 100*x^34 + 53*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 6*x^5 + 4*x^4 + 124*x^3 + 68*x^2 + 9*x + 92, x^41 + 76*x^39 + 124*x^38 + 118*x^37 + 20*x^36 + 124*x^35 + 4*x^34 + 37*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 54*x^5 + 52*x^4 + 92*x^3 + 100*x^2 + 121*x + 12, x^41 + 76*x^39 + 84*x^38 + 86*x^37 + 92*x^36 + 124*x^35 + 108*x^34 + 69*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 22*x^5 + 60*x^4 + 92*x^3 + 12*x^2 + 25*x + 68, x^41 + 76*x^39 + 104*x^38 + 110*x^37 + 8*x^36 + 12*x^35 + 120*x^34 + 93*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 110*x^5 + 72*x^4 + 108*x^3 + 56*x^2 + 113*x + 88, x^41 + 76*x^39 + 112*x^38 + 126*x^37 + 48*x^36 + 44*x^35 + 16*x^34 + 45*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 126*x^5 + 48*x^4 + 12*x^3 + 16*x^2 + 65*x + 80, x^41 + 76*x^39 + 44*x^38 + 118*x^37 + 4*x^36 + 124*x^35 + 20*x^34 + 37*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 54*x^5 + 36*x^4 + 92*x^3 + 116*x^2 + 121*x + 92, x^41 + 76*x^39 + 24*x^38 + 94*x^37 + 104*x^36 + 44*x^35 + 104*x^34 + 77*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 94*x^5 + 40*x^4 + 12*x^3 + 40*x^2 + 97*x + 88, x^41 + 76*x^39 + 84*x^38 + 86*x^37 + 28*x^36 + 60*x^35 + 44*x^34 + 5*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 22*x^5 + 124*x^4 + 28*x^3 + 76*x^2 + 89*x + 68, x^41 + 76*x^39 + 46*x^37 + 48*x^36 + 76*x^35 + 32*x^34 + 93*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 46*x^5 + 48*x^4 + 44*x^3 + 32*x^2 + 113*x + 48, x^41 + 76*x^39 + 20*x^38 + 38*x^37 + 44*x^36 + 92*x^35 + 76*x^34 + 21*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 102*x^5 + 12*x^4 + 60*x^3 + 108*x^2 + 105*x + 84, x^41 + 76*x^39 + 12*x^38 + 102*x^37 + 20*x^36 + 28*x^35 + 20*x^34 + 21*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 38*x^5 + 52*x^4 + 124*x^3 + 116*x^2 + 105*x + 108, x^41 + 76*x^39 + 68*x^38 + 102*x^37 + 92*x^36 + 92*x^35 + 92*x^34 + 85*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 38*x^5 + 60*x^4 + 60*x^3 + 124*x^2 + 41*x + 100, x^41 + 76*x^39 + 72*x^38 + 110*x^37 + 8*x^36 + 12*x^35 + 88*x^34 + 93*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 110*x^5 + 72*x^4 + 108*x^3 + 24*x^2 + 113*x + 24, x^41 + 76*x^39 + 60*x^38 + 6*x^37 + 4*x^36 + 28*x^35 + 100*x^34 + 117*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 70*x^5 + 36*x^4 + 124*x^3 + 68*x^2 + 73*x + 124, x^41 + 76*x^39 + 56*x^38 + 110*x^37 + 56*x^36 + 12*x^35 + 40*x^34 + 93*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 110*x^5 + 120*x^4 + 108*x^3 + 104*x^2 + 113*x + 40, x^41 + 76*x^39 + 20*x^38 + 102*x^37 + 108*x^36 + 92*x^35 + 76*x^34 + 85*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 38*x^5 + 76*x^4 + 60*x^3 + 108*x^2 + 41*x + 20, x^41 + 76*x^39 + 12*x^38 + 54*x^37 + 100*x^36 + 124*x^35 + 52*x^34 + 101*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 118*x^5 + 4*x^4 + 92*x^3 + 20*x^2 + 57*x + 124, x^41 + 76*x^39 + 12*x^38 + 54*x^37 + 36*x^36 + 124*x^35 + 52*x^34 + 101*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 118*x^5 + 68*x^4 + 92*x^3 + 20*x^2 + 57*x + 60, x^41 + 76*x^39 + 60*x^38 + 86*x^37 + 52*x^36 + 124*x^35 + 68*x^34 + 69*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 22*x^5 + 84*x^4 + 92*x^3 + 36*x^2 + 25*x + 108, x^41 + 76*x^39 + 92*x^38 + 86*x^37 + 116*x^36 + 124*x^35 + 100*x^34 + 69*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 22*x^5 + 20*x^4 + 92*x^3 + 68*x^2 + 25*x + 108, x^41 + 76*x^39 + 120*x^38 + 110*x^37 + 120*x^36 + 12*x^35 + 104*x^34 + 93*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 110*x^5 + 56*x^4 + 108*x^3 + 40*x^2 + 113*x + 104, x^41 + 76*x^39 + 4*x^38 + 6*x^37 + 92*x^36 + 92*x^35 + 92*x^34 + 53*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 70*x^5 + 60*x^4 + 60*x^3 + 124*x^2 + 9*x + 36, x^41 + 76*x^39 + 112*x^38 + 30*x^37 + 48*x^36 + 44*x^35 + 80*x^34 + 13*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 30*x^5 + 48*x^4 + 12*x^3 + 80*x^2 + 33*x + 16, x^41 + 76*x^39 + 8*x^38 + 94*x^37 + 56*x^36 + 44*x^35 + 120*x^34 + 77*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 94*x^5 + 120*x^4 + 12*x^3 + 56*x^2 + 97*x + 8, x^41 + 76*x^39 + 12*x^38 + 118*x^37 + 4*x^36 + 124*x^35 + 116*x^34 + 37*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 54*x^5 + 36*x^4 + 92*x^3 + 84*x^2 + 121*x + 28, x^41 + 76*x^39 + 72*x^38 + 46*x^37 + 40*x^36 + 12*x^35 + 24*x^34 + 29*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 46*x^5 + 104*x^4 + 108*x^3 + 88*x^2 + 49*x + 56, x^41 + 76*x^39 + 80*x^38 + 126*x^37 + 112*x^36 + 108*x^35 + 48*x^34 + 109*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 126*x^5 + 112*x^4 + 76*x^3 + 48*x^2 + x + 16, x^41 + 76*x^39 + 24*x^38 + 62*x^37 + 104*x^36 + 44*x^35 + 40*x^34 + 109*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 62*x^5 + 40*x^4 + 12*x^3 + 104*x^2 + x + 24, x^41 + 76*x^39 + 108*x^38 + 102*x^37 + 116*x^36 + 92*x^35 + 116*x^34 + 85*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 38*x^5 + 20*x^4 + 60*x^3 + 84*x^2 + 41*x + 76, x^41 + 76*x^39 + 116*x^38 + 6*x^37 + 12*x^36 + 92*x^35 + 44*x^34 + 53*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 70*x^5 + 108*x^4 + 60*x^3 + 76*x^2 + 9*x + 52, x^41 + 76*x^39 + 16*x^38 + 78*x^37 + 96*x^36 + 12*x^35 + 16*x^34 + 125*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 78*x^5 + 96*x^4 + 108*x^3 + 16*x^2 + 17*x, x^41 + 76*x^39 + 32*x^38 + 110*x^37 + 16*x^36 + 76*x^35 + 29*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 110*x^5 + 16*x^4 + 44*x^3 + 49*x + 80, x^41 + 76*x^39 + 20*x^38 + 102*x^37 + 12*x^36 + 28*x^35 + 76*x^34 + 21*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 38*x^5 + 108*x^4 + 124*x^3 + 108*x^2 + 105*x + 116, x^41 + 76*x^39 + 112*x^38 + 78*x^37 + 32*x^36 + 76*x^35 + 48*x^34 + 61*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 78*x^5 + 32*x^4 + 44*x^3 + 48*x^2 + 81*x + 64, x^41 + 76*x^39 + 44*x^38 + 6*x^37 + 84*x^36 + 92*x^35 + 52*x^34 + 53*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 70*x^5 + 116*x^4 + 60*x^3 + 20*x^2 + 9*x + 108, x^41 + 76*x^39 + 44*x^38 + 86*x^37 + 68*x^36 + 124*x^35 + 84*x^34 + 69*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 22*x^5 + 100*x^4 + 92*x^3 + 52*x^2 + 25*x + 92, x^41 + 76*x^39 + 32*x^38 + 30*x^37 + 108*x^35 + 96*x^34 + 77*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 30*x^5 + 76*x^3 + 96*x^2 + 97*x, x^41 + 76*x^39 + 76*x^38 + 86*x^37 + 4*x^36 + 124*x^35 + 116*x^34 + 69*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 22*x^5 + 36*x^4 + 92*x^3 + 84*x^2 + 25*x + 92, x^41 + 76*x^39 + 64*x^38 + 94*x^37 + 96*x^36 + 108*x^35 + 64*x^34 + 13*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 94*x^5 + 96*x^4 + 76*x^3 + 64*x^2 + 33*x + 32, x^41 + 76*x^39 + 8*x^38 + 14*x^37 + 40*x^36 + 76*x^35 + 88*x^34 + 125*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 14*x^5 + 104*x^4 + 44*x^3 + 24*x^2 + 17*x + 56, x^41 + 76*x^39 + 20*x^38 + 118*x^37 + 92*x^36 + 124*x^35 + 108*x^34 + 37*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 54*x^5 + 60*x^4 + 92*x^3 + 12*x^2 + 121*x + 4, x^41 + 76*x^39 + 104*x^38 + 110*x^37 + 72*x^36 + 12*x^35 + 120*x^34 + 93*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 110*x^5 + 8*x^4 + 108*x^3 + 56*x^2 + 113*x + 24, x^41 + 76*x^39 + 52*x^38 + 86*x^37 + 124*x^36 + 124*x^35 + 12*x^34 + 69*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 22*x^5 + 92*x^4 + 92*x^3 + 44*x^2 + 25*x + 36, x^41 + 76*x^39 + 84*x^38 + 86*x^37 + 92*x^36 + 60*x^35 + 44*x^34 + 5*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 22*x^5 + 60*x^4 + 28*x^3 + 76*x^2 + 89*x + 4, x^41 + 76*x^39 + 64*x^38 + 78*x^37 + 16*x^36 + 12*x^35 + 32*x^34 + 125*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 78*x^5 + 16*x^4 + 108*x^3 + 32*x^2 + 17*x + 16, x^41 + 76*x^39 + 84*x^38 + 6*x^37 + 12*x^36 + 28*x^35 + 76*x^34 + 117*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 70*x^5 + 108*x^4 + 124*x^3 + 108*x^2 + 73*x + 52, x^41 + 76*x^39 + 84*x^38 + 70*x^37 + 12*x^36 + 28*x^35 + 76*x^34 + 53*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 6*x^5 + 108*x^4 + 124*x^3 + 108*x^2 + 9*x + 52, x^41 + 76*x^39 + 12*x^38 + 102*x^37 + 84*x^36 + 28*x^35 + 20*x^34 + 21*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 38*x^5 + 116*x^4 + 124*x^3 + 116*x^2 + 105*x + 44, x^41 + 76*x^39 + 20*x^38 + 6*x^37 + 12*x^36 + 92*x^35 + 76*x^34 + 53*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 70*x^5 + 108*x^4 + 60*x^3 + 108*x^2 + 9*x + 116, x^41 + 76*x^39 + 96*x^38 + 126*x^37 + 44*x^35 + 32*x^34 + 45*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 126*x^5 + 12*x^3 + 32*x^2 + 65*x, x^41 + 76*x^39 + 92*x^38 + 102*x^37 + 36*x^36 + 28*x^35 + 4*x^34 + 21*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 38*x^5 + 68*x^4 + 124*x^3 + 100*x^2 + 105*x + 28, x^41 + 76*x^39 + 52*x^38 + 102*x^37 + 108*x^36 + 92*x^35 + 108*x^34 + 85*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 38*x^5 + 76*x^4 + 60*x^3 + 12*x^2 + 41*x + 84, x^41 + 76*x^39 + 60*x^38 + 6*x^37 + 36*x^36 + 92*x^35 + 100*x^34 + 53*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 70*x^5 + 68*x^4 + 60*x^3 + 68*x^2 + 9*x + 92, x^41 + 76*x^39 + 108*x^38 + 54*x^37 + 68*x^36 + 124*x^35 + 84*x^34 + 101*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 118*x^5 + 100*x^4 + 92*x^3 + 52*x^2 + 57*x + 28, x^41 + 76*x^39 + 12*x^38 + 118*x^37 + 68*x^36 + 124*x^35 + 116*x^34 + 37*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 54*x^5 + 100*x^4 + 92*x^3 + 84*x^2 + 121*x + 92, x^41 + 76*x^39 + 24*x^38 + 94*x^37 + 104*x^36 + 108*x^35 + 40*x^34 + 13*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 94*x^5 + 40*x^4 + 76*x^3 + 104*x^2 + 33*x + 24, x^41 + 76*x^39 + 92*x^38 + 102*x^37 + 4*x^36 + 28*x^35 + 68*x^34 + 21*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 38*x^5 + 36*x^4 + 124*x^3 + 36*x^2 + 105*x + 124, x^41 + 76*x^39 + 92*x^38 + 102*x^37 + 36*x^36 + 92*x^35 + 68*x^34 + 85*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 38*x^5 + 68*x^4 + 60*x^3 + 36*x^2 + 41*x + 92, x^41 + 76*x^39 + 48*x^38 + 126*x^37 + 112*x^36 + 44*x^35 + 80*x^34 + 45*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 126*x^5 + 112*x^4 + 12*x^3 + 80*x^2 + 65*x + 16, x^41 + 76*x^39 + 120*x^38 + 62*x^37 + 8*x^36 + 44*x^35 + 72*x^34 + 109*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 62*x^5 + 72*x^4 + 12*x^3 + 8*x^2 + x + 120, x^41 + 76*x^39 + 88*x^38 + 94*x^37 + 8*x^36 + 44*x^35 + 104*x^34 + 77*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 94*x^5 + 72*x^4 + 12*x^3 + 40*x^2 + 97*x + 120, x^41 + 76*x^39 + 84*x^38 + 118*x^37 + 124*x^36 + 124*x^35 + 108*x^34 + 37*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 54*x^5 + 92*x^4 + 92*x^3 + 12*x^2 + 121*x + 36, x^41 + 76*x^39 + 24*x^38 + 46*x^37 + 56*x^36 + 76*x^35 + 72*x^34 + 93*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 46*x^5 + 120*x^4 + 44*x^3 + 8*x^2 + 113*x + 40, x^41 + 76*x^39 + 24*x^38 + 78*x^37 + 56*x^36 + 76*x^35 + 8*x^34 + 61*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 78*x^5 + 120*x^4 + 44*x^3 + 72*x^2 + 81*x + 104, x^41 + 76*x^39 + 108*x^38 + 102*x^37 + 52*x^36 + 28*x^35 + 52*x^34 + 21*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 38*x^5 + 84*x^4 + 124*x^3 + 20*x^2 + 105*x + 76, x^41 + 76*x^39 + 36*x^38 + 70*x^37 + 124*x^36 + 92*x^35 + 60*x^34 + 117*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 6*x^5 + 92*x^4 + 60*x^3 + 92*x^2 + 73*x + 4, x^41 + 76*x^39 + 92*x^38 + 70*x^37 + 100*x^36 + 92*x^35 + 4*x^34 + 117*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 6*x^5 + 4*x^4 + 60*x^3 + 100*x^2 + 73*x + 92, x^41 + 76*x^39 + 16*x^38 + 14*x^37 + 32*x^36 + 76*x^35 + 80*x^34 + 125*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 114*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 14*x^5 + 32*x^4 + 44*x^3 + 80*x^2 + 17*x, x^41 + 76*x^39 + 92*x^38 + 6*x^37 + 100*x^36 + 92*x^35 + 4*x^34 + 53*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 70*x^5 + 4*x^4 + 60*x^3 + 100*x^2 + 9*x + 92, x^41 + 76*x^39 + 68*x^38 + 22*x^37 + 44*x^36 + 60*x^35 + 60*x^34 + 69*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 86*x^5 + 12*x^4 + 28*x^3 + 92*x^2 + 25*x + 52, x^41 + 76*x^39 + 60*x^38 + 102*x^37 + 100*x^36 + 92*x^35 + 36*x^34 + 85*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 38*x^5 + 4*x^4 + 60*x^3 + 4*x^2 + 41*x + 92, x^41 + 76*x^39 + 28*x^38 + 118*x^37 + 84*x^36 + 124*x^35 + 36*x^34 + 37*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 54*x^5 + 116*x^4 + 92*x^3 + 4*x^2 + 121*x + 12, x^41 + 76*x^39 + 120*x^38 + 14*x^37 + 56*x^36 + 76*x^35 + 104*x^34 + 125*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 14*x^5 + 120*x^4 + 44*x^3 + 40*x^2 + 17*x + 40, x^41 + 76*x^39 + 28*x^38 + 70*x^37 + 36*x^36 + 28*x^35 + 4*x^34 + 53*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 6*x^5 + 68*x^4 + 124*x^3 + 100*x^2 + 9*x + 92, x^41 + 76*x^39 + 64*x^38 + 126*x^37 + 64*x^36 + 108*x^35 + 64*x^34 + 109*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 126*x^5 + 64*x^4 + 76*x^3 + 64*x^2 + x + 64, x^41 + 76*x^39 + 28*x^38 + 86*x^37 + 84*x^36 + 60*x^35 + 36*x^34 + 5*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 22*x^5 + 116*x^4 + 28*x^3 + 4*x^2 + 89*x + 12, x^41 + 76*x^39 + 68*x^38 + 70*x^37 + 28*x^36 + 28*x^35 + 92*x^34 + 53*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 6*x^5 + 124*x^4 + 124*x^3 + 124*x^2 + 9*x + 36, x^41 + 76*x^39 + 36*x^38 + 102*x^37 + 124*x^36 + 28*x^35 + 60*x^34 + 21*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 38*x^5 + 92*x^4 + 124*x^3 + 92*x^2 + 105*x + 4, x^41 + 76*x^39 + 64*x^38 + 78*x^37 + 16*x^36 + 76*x^35 + 96*x^34 + 61*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 78*x^5 + 16*x^4 + 44*x^3 + 96*x^2 + 81*x + 80, x^41 + 76*x^39 + 20*x^38 + 86*x^37 + 92*x^36 + 60*x^35 + 108*x^34 + 5*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 22*x^5 + 60*x^4 + 28*x^3 + 12*x^2 + 89*x + 4, x^41 + 76*x^39 + 124*x^38 + 102*x^37 + 4*x^36 + 28*x^35 + 100*x^34 + 21*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 38*x^5 + 36*x^4 + 124*x^3 + 68*x^2 + 105*x + 60, x^41 + 76*x^39 + 12*x^38 + 86*x^37 + 36*x^36 + 124*x^35 + 116*x^34 + 69*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 22*x^5 + 68*x^4 + 92*x^3 + 84*x^2 + 25*x + 124, x^41 + 76*x^39 + 104*x^38 + 62*x^37 + 120*x^36 + 108*x^35 + 88*x^34 + 45*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 62*x^5 + 56*x^4 + 76*x^3 + 24*x^2 + 65*x + 8, x^41 + 76*x^39 + 16*x^38 + 78*x^37 + 64*x^36 + 76*x^35 + 16*x^34 + 61*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 78*x^5 + 64*x^4 + 44*x^3 + 16*x^2 + 81*x + 32, x^41 + 76*x^39 + 24*x^38 + 14*x^37 + 120*x^36 + 12*x^35 + 72*x^34 + 61*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 14*x^5 + 56*x^4 + 108*x^3 + 8*x^2 + 81*x + 104, x^41 + 76*x^39 + 72*x^38 + 110*x^37 + 104*x^36 + 76*x^35 + 88*x^34 + 29*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 110*x^5 + 40*x^4 + 44*x^3 + 24*x^2 + 49*x + 56, x^41 + 76*x^39 + 112*x^38 + 30*x^37 + 48*x^36 + 108*x^35 + 16*x^34 + 77*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 30*x^5 + 48*x^4 + 76*x^3 + 16*x^2 + 97*x + 80, x^41 + 76*x^39 + 80*x^38 + 126*x^37 + 112*x^36 + 44*x^35 + 112*x^34 + 45*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 126*x^5 + 112*x^4 + 12*x^3 + 112*x^2 + 65*x + 80, x^41 + 76*x^39 + 96*x^38 + 94*x^37 + 32*x^36 + 44*x^35 + 32*x^34 + 77*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 94*x^5 + 32*x^4 + 12*x^3 + 32*x^2 + 97*x + 96, x^41 + 76*x^39 + 116*x^38 + 118*x^37 + 124*x^36 + 124*x^35 + 12*x^34 + 37*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 54*x^5 + 92*x^4 + 92*x^3 + 44*x^2 + 121*x + 100, x^41 + 76*x^39 + 24*x^38 + 62*x^37 + 40*x^36 + 44*x^35 + 40*x^34 + 109*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 62*x^5 + 104*x^4 + 12*x^3 + 104*x^2 + x + 88, x^41 + 76*x^39 + 124*x^38 + 70*x^37 + 100*x^36 + 92*x^35 + 36*x^34 + 117*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 6*x^5 + 4*x^4 + 60*x^3 + 4*x^2 + 73*x + 28, x^41 + 76*x^39 + 36*x^38 + 70*x^37 + 28*x^36 + 92*x^35 + 124*x^34 + 117*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 6*x^5 + 124*x^4 + 60*x^3 + 28*x^2 + 73*x + 36, x^41 + 76*x^39 + 60*x^38 + 54*x^37 + 52*x^36 + 60*x^35 + 68*x^34 + 37*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 118*x^5 + 84*x^4 + 28*x^3 + 36*x^2 + 121*x + 108, x^41 + 76*x^39 + 64*x^38 + 110*x^37 + 48*x^36 + 76*x^35 + 96*x^34 + 29*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 110*x^5 + 48*x^4 + 44*x^3 + 96*x^2 + 49*x + 48, x^41 + 76*x^39 + 104*x^38 + 126*x^37 + 120*x^36 + 108*x^35 + 88*x^34 + 109*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 126*x^5 + 56*x^4 + 76*x^3 + 24*x^2 + x + 8, x^41 + 76*x^39 + 68*x^38 + 70*x^37 + 28*x^36 + 92*x^35 + 28*x^34 + 117*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 6*x^5 + 124*x^4 + 60*x^3 + 60*x^2 + 73*x + 100, x^41 + 76*x^39 + 44*x^38 + 102*x^37 + 116*x^36 + 28*x^35 + 116*x^34 + 21*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 38*x^5 + 20*x^4 + 124*x^3 + 84*x^2 + 105*x + 12, x^41 + 76*x^39 + 100*x^38 + 54*x^37 + 12*x^36 + 124*x^35 + 28*x^34 + 101*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 118*x^5 + 108*x^4 + 92*x^3 + 60*x^2 + 57*x + 84, x^41 + 76*x^39 + 8*x^38 + 46*x^37 + 8*x^36 + 12*x^35 + 24*x^34 + 29*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 46*x^5 + 72*x^4 + 108*x^3 + 88*x^2 + 49*x + 24, x^41 + 76*x^39 + 88*x^38 + 126*x^37 + 40*x^36 + 108*x^35 + 40*x^34 + 109*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 126*x^5 + 104*x^4 + 76*x^3 + 104*x^2 + x + 24, x^41 + 76*x^39 + 92*x^38 + 86*x^37 + 52*x^36 + 60*x^35 + 36*x^34 + 5*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 22*x^5 + 84*x^4 + 28*x^3 + 4*x^2 + 89*x + 108, x^41 + 76*x^39 + 120*x^38 + 30*x^37 + 40*x^36 + 108*x^35 + 8*x^34 + 77*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 30*x^5 + 104*x^4 + 76*x^3 + 72*x^2 + 97*x + 24, x^41 + 76*x^39 + 12*x^38 + 38*x^37 + 84*x^36 + 92*x^35 + 84*x^34 + 21*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 102*x^5 + 116*x^4 + 60*x^3 + 52*x^2 + 105*x + 108, x^41 + 76*x^39 + 72*x^38 + 30*x^37 + 56*x^36 + 44*x^35 + 56*x^34 + 13*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 30*x^5 + 120*x^4 + 12*x^3 + 120*x^2 + 33*x + 8, x^41 + 76*x^39 + 48*x^38 + 94*x^37 + 80*x^36 + 44*x^35 + 80*x^34 + 77*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 94*x^5 + 80*x^4 + 12*x^3 + 80*x^2 + 97*x + 48, x^41 + 76*x^39 + 100*x^38 + 54*x^37 + 44*x^36 + 60*x^35 + 28*x^34 + 37*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 118*x^5 + 12*x^4 + 28*x^3 + 60*x^2 + 121*x + 52, x^41 + 76*x^39 + 116*x^38 + 70*x^37 + 44*x^36 + 28*x^35 + 44*x^34 + 53*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 6*x^5 + 12*x^4 + 124*x^3 + 76*x^2 + 9*x + 20, x^41 + 76*x^39 + 80*x^38 + 94*x^37 + 48*x^36 + 108*x^35 + 112*x^34 + 13*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 94*x^5 + 48*x^4 + 76*x^3 + 112*x^2 + 33*x + 16, x^41 + 76*x^39 + 44*x^38 + 54*x^37 + 68*x^36 + 60*x^35 + 84*x^34 + 37*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 118*x^5 + 100*x^4 + 28*x^3 + 52*x^2 + 121*x + 92, x^41 + 76*x^39 + 20*x^38 + 118*x^37 + 28*x^36 + 124*x^35 + 108*x^34 + 37*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 54*x^5 + 124*x^4 + 92*x^3 + 12*x^2 + 121*x + 68, x^41 + 76*x^39 + 68*x^38 + 102*x^37 + 92*x^36 + 28*x^35 + 28*x^34 + 21*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 38*x^5 + 60*x^4 + 124*x^3 + 60*x^2 + 105*x + 36, x^41 + 76*x^39 + 64*x^38 + 78*x^37 + 80*x^36 + 76*x^35 + 96*x^34 + 61*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 78*x^5 + 80*x^4 + 44*x^3 + 96*x^2 + 81*x + 16, x^41 + 76*x^39 + 20*x^38 + 54*x^37 + 124*x^36 + 60*x^35 + 108*x^34 + 37*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 118*x^5 + 92*x^4 + 28*x^3 + 12*x^2 + 121*x + 100, x^41 + 76*x^39 + 100*x^38 + 22*x^37 + 76*x^36 + 60*x^35 + 28*x^34 + 69*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 86*x^5 + 44*x^4 + 28*x^3 + 60*x^2 + 25*x + 20, x^41 + 76*x^39 + 78*x^37 + 48*x^36 + 12*x^35 + 32*x^34 + 125*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 78*x^5 + 48*x^4 + 108*x^3 + 32*x^2 + 17*x + 48, x^41 + 76*x^39 + 48*x^38 + 14*x^37 + 64*x^36 + 12*x^35 + 112*x^34 + 61*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 14*x^5 + 64*x^4 + 108*x^3 + 112*x^2 + 81*x + 32, x^41 + 76*x^39 + 52*x^38 + 54*x^37 + 124*x^36 + 60*x^35 + 12*x^34 + 37*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 118*x^5 + 92*x^4 + 28*x^3 + 44*x^2 + 121*x + 36, x^41 + 76*x^39 + 116*x^38 + 102*x^37 + 108*x^36 + 28*x^35 + 108*x^34 + 21*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 38*x^5 + 76*x^4 + 124*x^3 + 12*x^2 + 105*x + 20, x^41 + 76*x^39 + 20*x^38 + 22*x^37 + 124*x^36 + 124*x^35 + 108*x^34 + 5*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 86*x^5 + 92*x^4 + 92*x^3 + 12*x^2 + 89*x + 100, x^41 + 76*x^39 + 68*x^38 + 102*x^37 + 124*x^36 + 92*x^35 + 28*x^34 + 85*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 38*x^5 + 92*x^4 + 60*x^3 + 60*x^2 + 41*x + 4, x^41 + 76*x^39 + 124*x^38 + 6*x^37 + 100*x^36 + 28*x^35 + 100*x^34 + 117*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 70*x^5 + 4*x^4 + 124*x^3 + 68*x^2 + 73*x + 92, x^41 + 76*x^39 + 116*x^38 + 86*x^37 + 92*x^36 + 60*x^35 + 76*x^34 + 5*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 22*x^5 + 60*x^4 + 28*x^3 + 108*x^2 + 89*x + 68, x^41 + 76*x^39 + 92*x^38 + 70*x^37 + 4*x^36 + 28*x^35 + 4*x^34 + 53*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 6*x^5 + 36*x^4 + 124*x^3 + 100*x^2 + 9*x + 60, x^41 + 76*x^39 + 112*x^38 + 30*x^37 + 112*x^36 + 108*x^35 + 16*x^34 + 77*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 30*x^5 + 112*x^4 + 76*x^3 + 16*x^2 + 97*x + 16, x^41 + 76*x^39 + 112*x^38 + 78*x^37 + 64*x^36 + 12*x^35 + 48*x^34 + 125*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 78*x^5 + 64*x^4 + 108*x^3 + 48*x^2 + 17*x + 32, x^41 + 76*x^39 + 30*x^37 + 108*x^35 + 64*x^34 + 77*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 30*x^5 + 76*x^3 + 64*x^2 + 97*x + 64, x^41 + 76*x^39 + 64*x^38 + 126*x^37 + 44*x^35 + 45*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 52*x^21 + 40*x^19 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 126*x^5 + 12*x^3 + 65*x + 64, x^41 + 76*x^39 + 36*x^38 + 6*x^37 + 28*x^36 + 92*x^35 + 124*x^34 + 53*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 70*x^5 + 124*x^4 + 60*x^3 + 28*x^2 + 9*x + 36, x^41 + 76*x^39 + 88*x^38 + 62*x^37 + 8*x^36 + 44*x^35 + 40*x^34 + 109*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 62*x^5 + 72*x^4 + 12*x^3 + 104*x^2 + x + 56, x^41 + 76*x^39 + 64*x^38 + 46*x^37 + 112*x^36 + 12*x^35 + 32*x^34 + 29*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 46*x^5 + 112*x^4 + 108*x^3 + 32*x^2 + 49*x + 48, x^41 + 76*x^39 + 72*x^38 + 30*x^37 + 88*x^36 + 108*x^35 + 56*x^34 + 77*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 30*x^5 + 24*x^4 + 76*x^3 + 120*x^2 + 97*x + 104, x^41 + 76*x^39 + 116*x^38 + 38*x^37 + 44*x^36 + 28*x^35 + 108*x^34 + 85*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 102*x^5 + 12*x^4 + 124*x^3 + 12*x^2 + 41*x + 84, x^41 + 76*x^39 + 92*x^38 + 54*x^37 + 20*x^36 + 124*x^35 + 100*x^34 + 101*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 118*x^5 + 52*x^4 + 92*x^3 + 68*x^2 + 57*x + 76, x^41 + 76*x^39 + 80*x^38 + 46*x^37 + 96*x^36 + 76*x^35 + 80*x^34 + 93*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 46*x^5 + 96*x^4 + 44*x^3 + 80*x^2 + 113*x, x^41 + 76*x^39 + 40*x^38 + 126*x^37 + 56*x^36 + 44*x^35 + 88*x^34 + 45*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 126*x^5 + 120*x^4 + 12*x^3 + 24*x^2 + 65*x + 8, x^41 + 76*x^39 + 72*x^38 + 46*x^37 + 40*x^36 + 76*x^35 + 88*x^34 + 93*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 46*x^5 + 104*x^4 + 44*x^3 + 24*x^2 + 113*x + 120, x^41 + 76*x^39 + 4*x^38 + 118*x^37 + 108*x^36 + 60*x^35 + 60*x^34 + 101*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 54*x^5 + 76*x^4 + 28*x^3 + 92*x^2 + 57*x + 52, x^41 + 76*x^39 + 64*x^38 + 30*x^37 + 108*x^35 + 77*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 30*x^5 + 76*x^3 + 97*x + 64, x^41 + 76*x^39 + 44*x^38 + 22*x^37 + 36*x^36 + 60*x^35 + 84*x^34 + 69*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 86*x^5 + 68*x^4 + 28*x^3 + 52*x^2 + 25*x + 124, x^41 + 76*x^39 + 20*x^38 + 118*x^37 + 60*x^36 + 60*x^35 + 108*x^34 + 101*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 54*x^5 + 28*x^4 + 28*x^3 + 12*x^2 + 57*x + 36, x^41 + 76*x^39 + 108*x^38 + 22*x^37 + 4*x^36 + 60*x^35 + 84*x^34 + 69*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 86*x^5 + 36*x^4 + 28*x^3 + 52*x^2 + 25*x + 92, x^41 + 76*x^39 + 28*x^38 + 38*x^37 + 100*x^36 + 28*x^35 + 68*x^34 + 85*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 102*x^5 + 4*x^4 + 124*x^3 + 36*x^2 + 41*x + 92, x^41 + 76*x^39 + 52*x^38 + 102*x^37 + 108*x^36 + 28*x^35 + 44*x^34 + 21*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 38*x^5 + 76*x^4 + 124*x^3 + 76*x^2 + 105*x + 20, x^41 + 76*x^39 + 72*x^38 + 110*x^37 + 72*x^36 + 12*x^35 + 88*x^34 + 93*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 110*x^5 + 8*x^4 + 108*x^3 + 24*x^2 + 113*x + 88, x^41 + 76*x^39 + 68*x^38 + 102*x^37 + 124*x^36 + 28*x^35 + 92*x^34 + 21*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 38*x^5 + 92*x^4 + 124*x^3 + 124*x^2 + 105*x + 68, x^41 + 76*x^39 + 20*x^38 + 6*x^37 + 108*x^36 + 28*x^35 + 76*x^34 + 117*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 70*x^5 + 76*x^4 + 124*x^3 + 108*x^2 + 73*x + 20, x^41 + 76*x^39 + 40*x^38 + 46*x^37 + 72*x^36 + 12*x^35 + 56*x^34 + 29*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 46*x^5 + 8*x^4 + 108*x^3 + 120*x^2 + 49*x + 24, x^41 + 76*x^39 + 20*x^38 + 70*x^37 + 108*x^36 + 28*x^35 + 76*x^34 + 53*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 6*x^5 + 76*x^4 + 124*x^3 + 108*x^2 + 9*x + 20, x^41 + 76*x^39 + 88*x^38 + 62*x^37 + 8*x^36 + 108*x^35 + 104*x^34 + 45*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 62*x^5 + 72*x^4 + 76*x^3 + 40*x^2 + 65*x + 120, x^41 + 76*x^39 + 100*x^38 + 54*x^37 + 108*x^36 + 60*x^35 + 28*x^34 + 37*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 118*x^5 + 76*x^4 + 28*x^3 + 60*x^2 + 121*x + 116, x^41 + 76*x^39 + 78*x^37 + 48*x^36 + 76*x^35 + 96*x^34 + 61*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 78*x^5 + 48*x^4 + 44*x^3 + 96*x^2 + 81*x + 112, x^41 + 76*x^39 + 12*x^38 + 38*x^37 + 20*x^36 + 92*x^35 + 84*x^34 + 21*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 102*x^5 + 52*x^4 + 60*x^3 + 52*x^2 + 105*x + 44, x^41 + 76*x^39 + 56*x^38 + 94*x^37 + 8*x^36 + 108*x^35 + 8*x^34 + 13*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 94*x^5 + 72*x^4 + 76*x^3 + 72*x^2 + 33*x + 120, x^41 + 76*x^39 + 100*x^38 + 118*x^37 + 76*x^36 + 60*x^35 + 92*x^34 + 101*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 54*x^5 + 44*x^4 + 28*x^3 + 124*x^2 + 57*x + 84, x^41 + 76*x^39 + 92*x^38 + 86*x^37 + 20*x^36 + 124*x^35 + 36*x^34 + 69*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 22*x^5 + 52*x^4 + 92*x^3 + 4*x^2 + 25*x + 12, x^41 + 76*x^39 + 88*x^38 + 110*x^37 + 120*x^36 + 12*x^35 + 72*x^34 + 93*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 110*x^5 + 56*x^4 + 108*x^3 + 8*x^2 + 113*x + 40, x^41 + 76*x^39 + 8*x^38 + 62*x^37 + 88*x^36 + 44*x^35 + 120*x^34 + 109*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 62*x^5 + 24*x^4 + 12*x^3 + 56*x^2 + x + 104, x^41 + 76*x^39 + 24*x^38 + 110*x^37 + 88*x^36 + 76*x^35 + 8*x^34 + 29*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 110*x^5 + 24*x^4 + 44*x^3 + 72*x^2 + 49*x + 72, x^41 + 76*x^39 + 12*x^38 + 54*x^37 + 36*x^36 + 60*x^35 + 116*x^34 + 37*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 118*x^5 + 68*x^4 + 28*x^3 + 84*x^2 + 121*x + 124, x^41 + 76*x^39 + 60*x^38 + 70*x^37 + 4*x^36 + 28*x^35 + 100*x^34 + 53*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 6*x^5 + 36*x^4 + 124*x^3 + 68*x^2 + 9*x + 124, x^41 + 76*x^39 + 52*x^38 + 54*x^37 + 92*x^36 + 124*x^35 + 12*x^34 + 101*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 118*x^5 + 60*x^4 + 92*x^3 + 44*x^2 + 57*x + 68, x^41 + 76*x^39 + 68*x^38 + 38*x^37 + 92*x^36 + 92*x^35 + 92*x^34 + 21*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 102*x^5 + 60*x^4 + 60*x^3 + 124*x^2 + 105*x + 100, x^41 + 76*x^39 + 4*x^38 + 86*x^37 + 12*x^36 + 60*x^35 + 60*x^34 + 5*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 22*x^5 + 108*x^4 + 28*x^3 + 92*x^2 + 89*x + 20, x^41 + 76*x^39 + 20*x^38 + 86*x^37 + 124*x^36 + 124*x^35 + 108*x^34 + 69*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 22*x^5 + 92*x^4 + 92*x^3 + 12*x^2 + 25*x + 100, x^41 + 76*x^39 + 24*x^38 + 78*x^37 + 24*x^36 + 12*x^35 + 8*x^34 + 125*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 78*x^5 + 88*x^4 + 108*x^3 + 72*x^2 + 17*x + 8, x^41 + 76*x^39 + 60*x^38 + 54*x^37 + 84*x^36 + 124*x^35 + 68*x^34 + 101*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 118*x^5 + 116*x^4 + 92*x^3 + 36*x^2 + 57*x + 76, x^41 + 76*x^39 + 24*x^38 + 126*x^37 + 8*x^36 + 44*x^35 + 104*x^34 + 45*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 126*x^5 + 72*x^4 + 12*x^3 + 40*x^2 + 65*x + 56, x^41 + 76*x^39 + 16*x^38 + 110*x^37 + 32*x^36 + 12*x^35 + 80*x^34 + 93*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 110*x^5 + 32*x^4 + 108*x^3 + 80*x^2 + 113*x, x^41 + 76*x^39 + 24*x^38 + 78*x^37 + 56*x^36 + 12*x^35 + 72*x^34 + 125*x^33 + 104*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 78*x^5 + 120*x^4 + 108*x^3 + 8*x^2 + 17*x + 40, x^41 + 76*x^39 + 56*x^38 + 78*x^37 + 24*x^36 + 12*x^35 + 40*x^34 + 125*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 78*x^5 + 88*x^4 + 108*x^3 + 104*x^2 + 17*x + 72, x^41 + 76*x^39 + 4*x^38 + 22*x^37 + 108*x^36 + 60*x^35 + 124*x^34 + 69*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 86*x^5 + 76*x^4 + 28*x^3 + 28*x^2 + 25*x + 116, x^41 + 76*x^39 + 64*x^38 + 94*x^37 + 108*x^35 + 13*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 94*x^5 + 76*x^3 + 33*x + 64, x^41 + 76*x^39 + 108*x^38 + 6*x^37 + 84*x^36 + 92*x^35 + 116*x^34 + 53*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 70*x^5 + 116*x^4 + 60*x^3 + 84*x^2 + 9*x + 108, x^41 + 76*x^39 + 120*x^38 + 14*x^37 + 24*x^36 + 12*x^35 + 104*x^34 + 61*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 14*x^5 + 88*x^4 + 108*x^3 + 40*x^2 + 81*x + 72, x^41 + 76*x^39 + 16*x^38 + 30*x^37 + 16*x^36 + 44*x^35 + 48*x^34 + 13*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 30*x^5 + 16*x^4 + 12*x^3 + 48*x^2 + 33*x + 48, x^41 + 76*x^39 + 44*x^38 + 70*x^37 + 52*x^36 + 92*x^35 + 116*x^34 + 117*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 6*x^5 + 84*x^4 + 60*x^3 + 84*x^2 + 73*x + 76, x^41 + 76*x^39 + 120*x^38 + 126*x^37 + 8*x^36 + 108*x^35 + 8*x^34 + 109*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 126*x^5 + 72*x^4 + 76*x^3 + 72*x^2 + x + 56, x^41 + 76*x^39 + 4*x^38 + 6*x^37 + 60*x^36 + 28*x^35 + 92*x^34 + 117*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 70*x^5 + 28*x^4 + 124*x^3 + 124*x^2 + 73*x + 68, x^41 + 76*x^39 + 20*x^38 + 70*x^37 + 44*x^36 + 92*x^35 + 12*x^34 + 117*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 6*x^5 + 12*x^4 + 60*x^3 + 44*x^2 + 73*x + 20, x^41 + 76*x^39 + 8*x^38 + 14*x^37 + 104*x^36 + 12*x^35 + 24*x^34 + 61*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 14*x^5 + 40*x^4 + 108*x^3 + 88*x^2 + 81*x + 56, x^41 + 76*x^39 + 20*x^38 + 6*x^37 + 44*x^36 + 92*x^35 + 12*x^34 + 53*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 70*x^5 + 12*x^4 + 60*x^3 + 44*x^2 + 9*x + 20, x^41 + 76*x^39 + 32*x^38 + 46*x^37 + 16*x^36 + 12*x^35 + 64*x^34 + 29*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 46*x^5 + 16*x^4 + 108*x^3 + 64*x^2 + 49*x + 16, x^41 + 76*x^39 + 78*x^37 + 112*x^36 + 76*x^35 + 96*x^34 + 61*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 78*x^5 + 112*x^4 + 44*x^3 + 96*x^2 + 81*x + 48, x^41 + 76*x^39 + 108*x^38 + 102*x^37 + 84*x^36 + 28*x^35 + 116*x^34 + 21*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 38*x^5 + 116*x^4 + 124*x^3 + 84*x^2 + 105*x + 108, x^41 + 76*x^39 + 24*x^38 + 94*x^37 + 40*x^36 + 108*x^35 + 40*x^34 + 13*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 94*x^5 + 104*x^4 + 76*x^3 + 104*x^2 + 33*x + 88, x^41 + 76*x^39 + 112*x^38 + 94*x^37 + 80*x^36 + 44*x^35 + 16*x^34 + 77*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 94*x^5 + 80*x^4 + 12*x^3 + 16*x^2 + 97*x + 48, x^41 + 76*x^39 + 108*x^38 + 22*x^37 + 100*x^36 + 124*x^35 + 84*x^34 + 5*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 86*x^5 + 4*x^4 + 92*x^3 + 52*x^2 + 89*x + 124, x^41 + 76*x^39 + 4*x^38 + 54*x^37 + 12*x^36 + 60*x^35 + 124*x^34 + 37*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 118*x^5 + 108*x^4 + 28*x^3 + 28*x^2 + 121*x + 84, x^41 + 76*x^39 + 52*x^38 + 54*x^37 + 28*x^36 + 60*x^35 + 76*x^34 + 37*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 118*x^5 + 124*x^4 + 28*x^3 + 108*x^2 + 121*x + 68, x^41 + 76*x^39 + 32*x^38 + 14*x^37 + 48*x^36 + 12*x^35 + 64*x^34 + 61*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 14*x^5 + 48*x^4 + 108*x^3 + 64*x^2 + 81*x + 112, x^41 + 76*x^39 + 76*x^38 + 118*x^37 + 68*x^36 + 60*x^35 + 116*x^34 + 101*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 54*x^5 + 100*x^4 + 28*x^3 + 84*x^2 + 57*x + 28, x^41 + 76*x^39 + 124*x^38 + 54*x^37 + 52*x^36 + 124*x^35 + 68*x^34 + 101*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 118*x^5 + 84*x^4 + 92*x^3 + 36*x^2 + 57*x + 44, x^41 + 76*x^39 + 60*x^38 + 38*x^37 + 4*x^36 + 28*x^35 + 36*x^34 + 85*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 102*x^5 + 36*x^4 + 124*x^3 + 4*x^2 + 41*x + 60, x^41 + 76*x^39 + 68*x^38 + 102*x^37 + 28*x^36 + 92*x^35 + 92*x^34 + 85*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 38*x^5 + 124*x^4 + 60*x^3 + 124*x^2 + 41*x + 36, x^41 + 76*x^39 + 36*x^38 + 102*x^37 + 28*x^36 + 92*x^35 + 60*x^34 + 85*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 38*x^5 + 124*x^4 + 60*x^3 + 92*x^2 + 41*x + 100, x^41 + 76*x^39 + 36*x^38 + 38*x^37 + 60*x^36 + 28*x^35 + 60*x^34 + 85*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 102*x^5 + 28*x^4 + 124*x^3 + 92*x^2 + 41*x + 68, x^41 + 76*x^39 + 104*x^38 + 62*x^37 + 24*x^36 + 108*x^35 + 24*x^34 + 45*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 62*x^5 + 88*x^4 + 76*x^3 + 88*x^2 + 65*x + 40, x^41 + 76*x^39 + 116*x^38 + 22*x^37 + 28*x^36 + 60*x^35 + 76*x^34 + 69*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 86*x^5 + 124*x^4 + 28*x^3 + 108*x^2 + 25*x + 4, x^41 + 76*x^39 + 88*x^38 + 126*x^37 + 72*x^36 + 44*x^35 + 40*x^34 + 45*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 126*x^5 + 8*x^4 + 12*x^3 + 104*x^2 + 65*x + 120, x^41 + 76*x^39 + 76*x^38 + 6*x^37 + 20*x^36 + 28*x^35 + 20*x^34 + 117*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 70*x^5 + 52*x^4 + 124*x^3 + 116*x^2 + 73*x + 44, x^41 + 76*x^39 + 92*x^38 + 86*x^37 + 84*x^36 + 124*x^35 + 36*x^34 + 69*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 22*x^5 + 116*x^4 + 92*x^3 + 4*x^2 + 25*x + 76, x^41 + 76*x^39 + 76*x^38 + 70*x^37 + 20*x^36 + 28*x^35 + 20*x^34 + 53*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 6*x^5 + 52*x^4 + 124*x^3 + 116*x^2 + 9*x + 44, x^41 + 76*x^39 + 94*x^37 + 64*x^36 + 44*x^35 + 77*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 94*x^5 + 64*x^4 + 12*x^3 + 97*x + 64, x^41 + 76*x^39 + 100*x^38 + 102*x^37 + 60*x^36 + 92*x^35 + 60*x^34 + 85*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 38*x^5 + 28*x^4 + 60*x^3 + 92*x^2 + 41*x + 4, x^41 + 76*x^39 + 92*x^38 + 38*x^37 + 36*x^36 + 92*x^35 + 68*x^34 + 21*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 102*x^5 + 68*x^4 + 60*x^3 + 36*x^2 + 105*x + 92, x^41 + 76*x^39 + 76*x^38 + 54*x^37 + 68*x^36 + 60*x^35 + 116*x^34 + 37*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 118*x^5 + 100*x^4 + 28*x^3 + 84*x^2 + 121*x + 28, x^41 + 76*x^39 + 88*x^38 + 14*x^37 + 88*x^36 + 12*x^35 + 72*x^34 + 61*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 14*x^5 + 24*x^4 + 108*x^3 + 8*x^2 + 81*x + 72, x^41 + 76*x^39 + 16*x^38 + 110*x^37 + 32*x^36 + 76*x^35 + 16*x^34 + 29*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 16*x^6 + 110*x^5 + 32*x^4 + 44*x^3 + 16*x^2 + 49*x + 64, x^41 + 76*x^39 + 92*x^38 + 118*x^37 + 84*x^36 + 60*x^35 + 36*x^34 + 101*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 54*x^5 + 116*x^4 + 28*x^3 + 4*x^2 + 57*x + 76, x^41 + 76*x^39 + 56*x^38 + 126*x^37 + 104*x^36 + 44*x^35 + 72*x^34 + 45*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 126*x^5 + 40*x^4 + 12*x^3 + 8*x^2 + 65*x + 88, x^41 + 76*x^39 + 44*x^38 + 22*x^37 + 4*x^36 + 60*x^35 + 20*x^34 + 69*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 86*x^5 + 36*x^4 + 28*x^3 + 116*x^2 + 25*x + 92, x^41 + 76*x^39 + 108*x^38 + 118*x^37 + 68*x^36 + 60*x^35 + 20*x^34 + 101*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 54*x^5 + 100*x^4 + 28*x^3 + 116*x^2 + 57*x + 92, x^41 + 76*x^39 + 92*x^38 + 54*x^37 + 84*x^36 + 124*x^35 + 100*x^34 + 101*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 118*x^5 + 116*x^4 + 92*x^3 + 68*x^2 + 57*x + 12, x^41 + 76*x^39 + 68*x^38 + 22*x^37 + 108*x^36 + 60*x^35 + 60*x^34 + 69*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 86*x^5 + 76*x^4 + 28*x^3 + 92*x^2 + 25*x + 116, x^41 + 76*x^39 + 30*x^37 + 64*x^36 + 108*x^35 + 64*x^34 + 77*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 30*x^5 + 64*x^4 + 76*x^3 + 64*x^2 + 97*x, x^41 + 76*x^39 + 94*x^37 + 96*x^36 + 44*x^35 + 64*x^34 + 77*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 94*x^5 + 96*x^4 + 12*x^3 + 64*x^2 + 97*x + 96, x^41 + 76*x^39 + 56*x^38 + 94*x^37 + 104*x^36 + 44*x^35 + 8*x^34 + 77*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 94*x^5 + 40*x^4 + 12*x^3 + 72*x^2 + 97*x + 24, x^41 + 76*x^39 + 64*x^38 + 30*x^37 + 64*x^36 + 108*x^35 + 77*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 40*x^19 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 64*x^6 + 30*x^5 + 64*x^4 + 76*x^3 + 97*x, x^41 + 76*x^39 + 64*x^38 + 78*x^37 + 80*x^36 + 12*x^35 + 32*x^34 + 125*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 78*x^5 + 80*x^4 + 108*x^3 + 32*x^2 + 17*x + 80, x^41 + 76*x^39 + 88*x^38 + 94*x^37 + 40*x^36 + 108*x^35 + 104*x^34 + 13*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 94*x^5 + 104*x^4 + 76*x^3 + 40*x^2 + 33*x + 88, x^41 + 76*x^39 + 60*x^38 + 38*x^37 + 100*x^36 + 92*x^35 + 36*x^34 + 21*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 102*x^5 + 4*x^4 + 60*x^3 + 4*x^2 + 105*x + 92, x^41 + 76*x^39 + 116*x^38 + 118*x^37 + 124*x^36 + 60*x^35 + 76*x^34 + 101*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 54*x^5 + 92*x^4 + 28*x^3 + 108*x^2 + 57*x + 36, x^41 + 76*x^39 + 24*x^38 + 62*x^37 + 8*x^36 + 44*x^35 + 104*x^34 + 109*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 62*x^5 + 72*x^4 + 12*x^3 + 40*x^2 + x + 56, x^41 + 76*x^39 + 40*x^38 + 94*x^37 + 120*x^36 + 108*x^35 + 88*x^34 + 13*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 94*x^5 + 56*x^4 + 76*x^3 + 24*x^2 + 33*x + 72, x^41 + 76*x^39 + 108*x^38 + 38*x^37 + 84*x^36 + 92*x^35 + 52*x^34 + 21*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 102*x^5 + 116*x^4 + 60*x^3 + 20*x^2 + 105*x + 44, x^41 + 76*x^39 + 60*x^38 + 54*x^37 + 20*x^36 + 124*x^35 + 68*x^34 + 101*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 118*x^5 + 52*x^4 + 92*x^3 + 36*x^2 + 57*x + 12, x^41 + 76*x^39 + 88*x^38 + 94*x^37 + 8*x^36 + 108*x^35 + 40*x^34 + 13*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 94*x^5 + 72*x^4 + 76*x^3 + 104*x^2 + 33*x + 56, x^41 + 76*x^39 + 44*x^38 + 22*x^37 + 100*x^36 + 60*x^35 + 84*x^34 + 69*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 86*x^5 + 4*x^4 + 28*x^3 + 52*x^2 + 25*x + 60, x^41 + 76*x^39 + 68*x^38 + 54*x^37 + 12*x^36 + 124*x^35 + 124*x^34 + 101*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 118*x^5 + 108*x^4 + 92*x^3 + 28*x^2 + 57*x + 20, x^41 + 76*x^39 + 52*x^38 + 22*x^37 + 124*x^36 + 60*x^35 + 76*x^34 + 69*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 40*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 84*x^6 + 86*x^5 + 92*x^4 + 28*x^3 + 108*x^2 + 25*x + 100, x^41 + 76*x^39 + 76*x^38 + 118*x^37 + 36*x^36 + 60*x^35 + 52*x^34 + 101*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 54*x^5 + 68*x^4 + 28*x^3 + 20*x^2 + 57*x + 124, x^41 + 76*x^39 + 60*x^38 + 70*x^37 + 4*x^36 + 92*x^35 + 36*x^34 + 117*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 6*x^5 + 36*x^4 + 60*x^3 + 4*x^2 + 73*x + 60, x^41 + 76*x^39 + 60*x^38 + 6*x^37 + 4*x^36 + 92*x^35 + 36*x^34 + 53*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 70*x^5 + 36*x^4 + 60*x^3 + 4*x^2 + 9*x + 60, x^41 + 76*x^39 + 80*x^38 + 94*x^37 + 112*x^36 + 44*x^35 + 48*x^34 + 77*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 94*x^5 + 112*x^4 + 12*x^3 + 48*x^2 + 97*x + 16, x^41 + 76*x^39 + 72*x^38 + 78*x^37 + 104*x^36 + 76*x^35 + 24*x^34 + 61*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 78*x^5 + 40*x^4 + 44*x^3 + 88*x^2 + 81*x + 120, x^41 + 76*x^39 + 116*x^38 + 38*x^37 + 12*x^36 + 28*x^35 + 44*x^34 + 85*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 102*x^5 + 108*x^4 + 124*x^3 + 76*x^2 + 41*x + 52, x^41 + 76*x^39 + 68*x^38 + 54*x^37 + 108*x^36 + 124*x^35 + 60*x^34 + 101*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 118*x^5 + 76*x^4 + 92*x^3 + 92*x^2 + 57*x + 116, x^41 + 76*x^39 + 96*x^38 + 110*x^37 + 80*x^36 + 76*x^35 + 64*x^34 + 29*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 110*x^5 + 80*x^4 + 44*x^3 + 64*x^2 + 49*x + 16, x^41 + 76*x^39 + 112*x^38 + 46*x^37 + 32*x^36 + 12*x^35 + 48*x^34 + 29*x^33 + 64*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 46*x^5 + 32*x^4 + 108*x^3 + 48*x^2 + 49*x + 64, x^41 + 76*x^39 + 124*x^38 + 86*x^37 + 84*x^36 + 124*x^35 + 68*x^34 + 69*x^33 + 108*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 22*x^5 + 116*x^4 + 92*x^3 + 36*x^2 + 25*x + 12, x^41 + 76*x^39 + 112*x^38 + 46*x^37 + 96*x^36 + 12*x^35 + 48*x^34 + 29*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 32*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 46*x^5 + 96*x^4 + 108*x^3 + 48*x^2 + 49*x, x^41 + 76*x^39 + 104*x^38 + 46*x^37 + 104*x^36 + 12*x^35 + 56*x^34 + 29*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 46*x^5 + 40*x^4 + 108*x^3 + 120*x^2 + 49*x + 56, x^41 + 76*x^39 + 100*x^38 + 86*x^37 + 108*x^36 + 60*x^35 + 92*x^34 + 5*x^33 + 84*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 22*x^5 + 76*x^4 + 28*x^3 + 124*x^2 + 89*x + 52, x^41 + 76*x^39 + 96*x^38 + 78*x^37 + 16*x^36 + 76*x^35 + 61*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 78*x^5 + 16*x^4 + 44*x^3 + 81*x + 16, x^41 + 76*x^39 + 40*x^38 + 62*x^37 + 88*x^36 + 44*x^35 + 24*x^34 + 109*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 62*x^5 + 24*x^4 + 12*x^3 + 88*x^2 + x + 40, x^41 + 76*x^39 + 4*x^38 + 22*x^37 + 76*x^36 + 60*x^35 + 60*x^34 + 69*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 86*x^5 + 44*x^4 + 28*x^3 + 92*x^2 + 25*x + 84, x^41 + 76*x^39 + 88*x^38 + 14*x^37 + 24*x^36 + 12*x^35 + 72*x^34 + 61*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 14*x^5 + 88*x^4 + 108*x^3 + 8*x^2 + 81*x + 8, x^41 + 76*x^39 + 12*x^38 + 54*x^37 + 100*x^36 + 60*x^35 + 116*x^34 + 37*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 118*x^5 + 4*x^4 + 28*x^3 + 84*x^2 + 121*x + 60, x^41 + 76*x^39 + 68*x^38 + 118*x^37 + 12*x^36 + 124*x^35 + 124*x^34 + 37*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 54*x^5 + 108*x^4 + 92*x^3 + 28*x^2 + 121*x + 20, x^41 + 76*x^39 + 76*x^38 + 102*x^37 + 20*x^36 + 92*x^35 + 20*x^34 + 85*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 38*x^5 + 52*x^4 + 60*x^3 + 116*x^2 + 41*x + 44, x^41 + 76*x^39 + 28*x^38 + 70*x^37 + 100*x^36 + 92*x^35 + 68*x^34 + 117*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 6*x^5 + 4*x^4 + 60*x^3 + 36*x^2 + 73*x + 92, x^41 + 76*x^39 + 116*x^38 + 118*x^37 + 92*x^36 + 60*x^35 + 12*x^34 + 101*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 24*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 40*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 20*x^6 + 54*x^5 + 60*x^4 + 28*x^3 + 44*x^2 + 57*x + 4, x^41 + 76*x^39 + 24*x^38 + 94*x^37 + 40*x^36 + 44*x^35 + 104*x^34 + 77*x^33 + 88*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 94*x^5 + 104*x^4 + 12*x^3 + 40*x^2 + 97*x + 24, x^41 + 76*x^39 + 24*x^38 + 110*x^37 + 88*x^36 + 12*x^35 + 72*x^34 + 93*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 110*x^5 + 24*x^4 + 108*x^3 + 8*x^2 + 113*x + 8, x^41 + 76*x^39 + 20*x^38 + 38*x^37 + 12*x^36 + 28*x^35 + 76*x^34 + 85*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 102*x^5 + 108*x^4 + 124*x^3 + 108*x^2 + 41*x + 116, x^41 + 76*x^39 + 36*x^38 + 38*x^37 + 28*x^36 + 28*x^35 + 124*x^34 + 85*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 102*x^5 + 124*x^4 + 124*x^3 + 28*x^2 + 41*x + 36, x^41 + 76*x^39 + 124*x^38 + 118*x^37 + 20*x^36 + 60*x^35 + 68*x^34 + 101*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 92*x^6 + 54*x^5 + 52*x^4 + 28*x^3 + 36*x^2 + 57*x + 76, x^41 + 76*x^39 + 94*x^37 + 32*x^36 + 108*x^35 + 13*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 116*x^21 + 64*x^20 + 40*x^19 + 82*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 94*x^5 + 32*x^4 + 76*x^3 + 33*x + 96, x^41 + 76*x^39 + 60*x^38 + 118*x^37 + 116*x^36 + 60*x^35 + 68*x^34 + 101*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 54*x^5 + 20*x^4 + 28*x^3 + 36*x^2 + 57*x + 44, x^41 + 76*x^39 + 44*x^38 + 6*x^37 + 52*x^36 + 28*x^35 + 52*x^34 + 117*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 70*x^5 + 84*x^4 + 124*x^3 + 20*x^2 + 73*x + 12, x^41 + 76*x^39 + 4*x^38 + 70*x^37 + 124*x^36 + 92*x^35 + 28*x^34 + 117*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 36*x^6 + 6*x^5 + 92*x^4 + 60*x^3 + 60*x^2 + 73*x + 68, x^41 + 76*x^39 + 44*x^38 + 70*x^37 + 52*x^36 + 28*x^35 + 52*x^34 + 53*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 6*x^5 + 84*x^4 + 124*x^3 + 20*x^2 + 9*x + 12, x^41 + 76*x^39 + 32*x^38 + 46*x^37 + 48*x^36 + 12*x^35 + 29*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 46*x^5 + 48*x^4 + 108*x^3 + 49*x + 48, x^41 + 76*x^39 + 8*x^38 + 126*x^37 + 88*x^36 + 44*x^35 + 120*x^34 + 45*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 126*x^5 + 24*x^4 + 12*x^3 + 56*x^2 + 65*x + 104, x^41 + 76*x^39 + 32*x^38 + 110*x^37 + 48*x^36 + 12*x^35 + 93*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 32*x^20 + 104*x^19 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 110*x^5 + 48*x^4 + 108*x^3 + 113*x + 48, x^41 + 76*x^39 + 108*x^38 + 22*x^37 + 68*x^36 + 124*x^35 + 20*x^34 + 5*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 86*x^5 + 100*x^4 + 92*x^3 + 116*x^2 + 89*x + 92, x^41 + 76*x^39 + 32*x^38 + 94*x^37 + 64*x^36 + 44*x^35 + 32*x^34 + 77*x^33 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 94*x^5 + 64*x^4 + 12*x^3 + 32*x^2 + 97*x, x^41 + 76*x^39 + 124*x^38 + 38*x^37 + 68*x^36 + 92*x^35 + 36*x^34 + 21*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 102*x^5 + 100*x^4 + 60*x^3 + 4*x^2 + 105*x + 60, x^41 + 76*x^39 + 112*x^38 + 30*x^37 + 16*x^36 + 44*x^35 + 16*x^34 + 13*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 30*x^5 + 16*x^4 + 12*x^3 + 16*x^2 + 33*x + 112, x^41 + 76*x^39 + 112*x^38 + 94*x^37 + 48*x^36 + 108*x^35 + 16*x^34 + 13*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 94*x^5 + 48*x^4 + 76*x^3 + 16*x^2 + 33*x + 80, x^41 + 76*x^39 + 56*x^38 + 94*x^37 + 104*x^36 + 108*x^35 + 72*x^34 + 13*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 94*x^5 + 40*x^4 + 76*x^3 + 8*x^2 + 33*x + 88, x^41 + 76*x^39 + 104*x^38 + 14*x^37 + 104*x^36 + 12*x^35 + 120*x^34 + 61*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 14*x^5 + 40*x^4 + 108*x^3 + 56*x^2 + 81*x + 120, x^41 + 76*x^39 + 112*x^38 + 126*x^37 + 16*x^36 + 108*x^35 + 16*x^34 + 109*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 126*x^5 + 16*x^4 + 76*x^3 + 16*x^2 + x + 112, x^41 + 76*x^39 + 72*x^38 + 78*x^37 + 40*x^36 + 76*x^35 + 24*x^34 + 61*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 8*x^6 + 78*x^5 + 104*x^4 + 44*x^3 + 88*x^2 + 81*x + 56, x^41 + 76*x^39 + 64*x^38 + 110*x^37 + 112*x^36 + 76*x^35 + 96*x^34 + 29*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 110*x^5 + 112*x^4 + 44*x^3 + 96*x^2 + 49*x + 112, x^41 + 76*x^39 + 84*x^38 + 38*x^37 + 44*x^36 + 28*x^35 + 76*x^34 + 85*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 102*x^5 + 12*x^4 + 124*x^3 + 108*x^2 + 41*x + 20, x^41 + 76*x^39 + 40*x^38 + 46*x^37 + 8*x^36 + 76*x^35 + 120*x^34 + 93*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 46*x^5 + 72*x^4 + 44*x^3 + 56*x^2 + 113*x + 24, x^41 + 76*x^39 + 68*x^38 + 38*x^37 + 124*x^36 + 92*x^35 + 28*x^34 + 21*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 102*x^5 + 92*x^4 + 60*x^3 + 60*x^2 + 105*x + 4, x^41 + 76*x^39 + 12*x^38 + 70*x^37 + 116*x^36 + 28*x^35 + 20*x^34 + 53*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 6*x^5 + 20*x^4 + 124*x^3 + 116*x^2 + 9*x + 12, x^41 + 76*x^39 + 32*x^38 + 46*x^37 + 80*x^36 + 76*x^35 + 93*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 46*x^5 + 80*x^4 + 44*x^3 + 113*x + 16, x^41 + 76*x^39 + 68*x^38 + 6*x^37 + 28*x^36 + 28*x^35 + 92*x^34 + 117*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 70*x^5 + 124*x^4 + 124*x^3 + 124*x^2 + 73*x + 36, x^41 + 76*x^39 + 60*x^38 + 86*x^37 + 84*x^36 + 60*x^35 + 68*x^34 + 5*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 88*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 22*x^5 + 116*x^4 + 28*x^3 + 36*x^2 + 89*x + 76, x^41 + 76*x^39 + 48*x^38 + 78*x^37 + 76*x^35 + 48*x^34 + 61*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 78*x^5 + 44*x^3 + 48*x^2 + 81*x + 32, x^41 + 76*x^39 + 72*x^38 + 62*x^37 + 120*x^36 + 44*x^35 + 120*x^34 + 109*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 62*x^5 + 56*x^4 + 12*x^3 + 56*x^2 + x + 8, x^41 + 76*x^39 + 60*x^38 + 70*x^37 + 36*x^36 + 92*x^35 + 100*x^34 + 117*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 28*x^6 + 6*x^5 + 68*x^4 + 60*x^3 + 68*x^2 + 73*x + 92, x^41 + 76*x^39 + 84*x^38 + 22*x^37 + 28*x^36 + 60*x^35 + 44*x^34 + 69*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 86*x^5 + 124*x^4 + 28*x^3 + 76*x^2 + 25*x + 68, x^41 + 76*x^39 + 88*x^38 + 110*x^37 + 56*x^36 + 12*x^35 + 72*x^34 + 93*x^33 + 40*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 84*x^21 + 16*x^20 + 104*x^19 + 112*x^18 + 50*x^17 + 48*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 24*x^6 + 110*x^5 + 120*x^4 + 108*x^3 + 8*x^2 + 113*x + 104, x^41 + 76*x^39 + 84*x^38 + 102*x^37 + 108*x^36 + 92*x^35 + 12*x^34 + 85*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 38*x^5 + 76*x^4 + 60*x^3 + 44*x^2 + 41*x + 20, x^41 + 76*x^39 + 32*x^38 + 62*x^37 + 32*x^36 + 108*x^35 + 96*x^34 + 45*x^33 + 96*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 32*x^6 + 62*x^5 + 32*x^4 + 76*x^3 + 96*x^2 + 65*x + 96, x^41 + 76*x^39 + 12*x^38 + 86*x^37 + 68*x^36 + 124*x^35 + 52*x^34 + 69*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 22*x^5 + 100*x^4 + 92*x^3 + 20*x^2 + 25*x + 28, x^41 + 76*x^39 + 116*x^38 + 102*x^37 + 44*x^36 + 28*x^35 + 108*x^34 + 21*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 38*x^5 + 12*x^4 + 124*x^3 + 12*x^2 + 105*x + 84, x^41 + 76*x^39 + 4*x^38 + 86*x^37 + 12*x^36 + 124*x^35 + 124*x^34 + 69*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 22*x^5 + 108*x^4 + 92*x^3 + 28*x^2 + 25*x + 84, x^41 + 76*x^39 + 88*x^38 + 30*x^37 + 104*x^36 + 44*x^35 + 40*x^34 + 13*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 30*x^5 + 40*x^4 + 12*x^3 + 104*x^2 + 33*x + 88, x^41 + 76*x^39 + 68*x^38 + 70*x^37 + 60*x^36 + 28*x^35 + 28*x^34 + 53*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 36*x^21 + 8*x^20 + 72*x^19 + 8*x^18 + 2*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 6*x^5 + 28*x^4 + 124*x^3 + 60*x^2 + 9*x + 68, x^41 + 76*x^39 + 28*x^38 + 102*x^37 + 68*x^36 + 92*x^35 + 68*x^34 + 85*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 38*x^5 + 100*x^4 + 60*x^3 + 36*x^2 + 41*x + 124, x^41 + 76*x^39 + 78*x^37 + 112*x^36 + 12*x^35 + 32*x^34 + 125*x^33 + 112*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 20*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 78*x^5 + 112*x^4 + 108*x^3 + 32*x^2 + 17*x + 112, x^41 + 76*x^39 + 68*x^38 + 22*x^37 + 12*x^36 + 124*x^35 + 60*x^34 + 5*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 86*x^5 + 108*x^4 + 92*x^3 + 92*x^2 + 89*x + 84, x^41 + 76*x^39 + 108*x^38 + 54*x^37 + 36*x^36 + 60*x^35 + 84*x^34 + 37*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 68*x^21 + 56*x^20 + 8*x^19 + 24*x^18 + 34*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 76*x^6 + 118*x^5 + 68*x^4 + 28*x^3 + 52*x^2 + 121*x + 60, x^41 + 76*x^39 + 92*x^38 + 22*x^37 + 116*x^36 + 60*x^35 + 36*x^34 + 69*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 86*x^5 + 20*x^4 + 28*x^3 + 4*x^2 + 25*x + 44, x^41 + 76*x^39 + 100*x^38 + 86*x^37 + 12*x^36 + 124*x^35 + 92*x^34 + 69*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 22*x^5 + 108*x^4 + 92*x^3 + 124*x^2 + 25*x + 20, x^41 + 76*x^39 + 104*x^38 + 46*x^37 + 8*x^36 + 76*x^35 + 56*x^34 + 93*x^33 + 88*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 46*x^5 + 72*x^4 + 44*x^3 + 120*x^2 + 113*x + 24, x^41 + 76*x^39 + 64*x^38 + 46*x^37 + 80*x^36 + 76*x^35 + 32*x^34 + 93*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 96*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 46*x^5 + 80*x^4 + 44*x^3 + 32*x^2 + 113*x + 80, x^41 + 76*x^39 + 80*x^38 + 78*x^37 + 64*x^36 + 76*x^35 + 80*x^34 + 61*x^33 + 32*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 20*x^21 + 104*x^19 + 96*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 78*x^5 + 64*x^4 + 44*x^3 + 80*x^2 + 81*x + 32, x^41 + 76*x^39 + 40*x^38 + 126*x^37 + 24*x^36 + 44*x^35 + 24*x^34 + 45*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 126*x^5 + 88*x^4 + 12*x^3 + 88*x^2 + 65*x + 104, x^41 + 76*x^39 + 16*x^38 + 94*x^37 + 48*x^36 + 108*x^35 + 48*x^34 + 13*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 116*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 82*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 94*x^5 + 48*x^4 + 76*x^3 + 48*x^2 + 33*x + 16, x^41 + 76*x^39 + 92*x^38 + 38*x^37 + 68*x^36 + 28*x^35 + 68*x^34 + 85*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 102*x^5 + 100*x^4 + 124*x^3 + 36*x^2 + 41*x + 60, x^41 + 76*x^39 + 124*x^38 + 38*x^37 + 100*x^36 + 28*x^35 + 36*x^34 + 85*x^33 + 124*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 120*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 102*x^5 + 4*x^4 + 124*x^3 + 4*x^2 + 41*x + 28, x^41 + 76*x^39 + 12*x^38 + 70*x^37 + 84*x^36 + 92*x^35 + 20*x^34 + 117*x^33 + 12*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 6*x^5 + 116*x^4 + 60*x^3 + 116*x^2 + 73*x + 44, x^41 + 76*x^39 + 68*x^38 + 38*x^37 + 28*x^36 + 28*x^35 + 28*x^34 + 85*x^33 + 4*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 120*x^22 + 100*x^21 + 72*x^20 + 72*x^19 + 8*x^18 + 66*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 100*x^6 + 102*x^5 + 124*x^4 + 124*x^3 + 60*x^2 + 41*x + 100, x^41 + 76*x^39 + 120*x^38 + 30*x^37 + 72*x^36 + 44*x^35 + 8*x^34 + 13*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 56*x^6 + 30*x^5 + 8*x^4 + 12*x^3 + 72*x^2 + 33*x + 120, x^41 + 76*x^39 + 112*x^38 + 46*x^37 + 76*x^35 + 48*x^34 + 93*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 84*x^21 + 104*x^19 + 32*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 112*x^6 + 46*x^5 + 44*x^3 + 48*x^2 + 113*x + 96, x^41 + 76*x^39 + 64*x^38 + 46*x^37 + 48*x^36 + 76*x^35 + 96*x^34 + 93*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 84*x^21 + 32*x^20 + 104*x^19 + 64*x^18 + 50*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 64*x^6 + 46*x^5 + 48*x^4 + 44*x^3 + 96*x^2 + 113*x + 48, x^41 + 76*x^39 + 36*x^38 + 54*x^37 + 44*x^36 + 124*x^35 + 28*x^34 + 101*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 118*x^5 + 12*x^4 + 92*x^3 + 60*x^2 + 57*x + 116, x^41 + 76*x^39 + 44*x^38 + 86*x^37 + 4*x^36 + 60*x^35 + 20*x^34 + 5*x^33 + 60*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 22*x^5 + 36*x^4 + 28*x^3 + 116*x^2 + 89*x + 92, x^41 + 76*x^39 + 96*x^38 + 126*x^37 + 64*x^36 + 44*x^35 + 32*x^34 + 45*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 40*x^19 + 64*x^18 + 18*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 126*x^5 + 64*x^4 + 12*x^3 + 32*x^2 + 65*x + 64, x^41 + 76*x^39 + 108*x^38 + 38*x^37 + 116*x^36 + 28*x^35 + 52*x^34 + 85*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 76*x^6 + 102*x^5 + 20*x^4 + 124*x^3 + 20*x^2 + 41*x + 12, x^41 + 76*x^39 + 20*x^38 + 102*x^37 + 12*x^36 + 92*x^35 + 12*x^34 + 85*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 38*x^5 + 108*x^4 + 60*x^3 + 44*x^2 + 41*x + 52, x^41 + 76*x^39 + 36*x^38 + 118*x^37 + 76*x^36 + 60*x^35 + 28*x^34 + 101*x^33 + 116*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 54*x^5 + 44*x^4 + 28*x^3 + 60*x^2 + 57*x + 84, x^41 + 76*x^39 + 120*x^38 + 46*x^37 + 88*x^36 + 12*x^35 + 40*x^34 + 29*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 46*x^5 + 24*x^4 + 108*x^3 + 104*x^2 + 49*x + 72, x^41 + 76*x^39 + 40*x^38 + 94*x^37 + 56*x^36 + 44*x^35 + 24*x^34 + 77*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 94*x^5 + 120*x^4 + 12*x^3 + 88*x^2 + 97*x + 72, x^41 + 76*x^39 + 8*x^38 + 110*x^37 + 8*x^36 + 76*x^35 + 88*x^34 + 29*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 110*x^5 + 72*x^4 + 44*x^3 + 24*x^2 + 49*x + 88, x^41 + 76*x^39 + 104*x^38 + 62*x^37 + 56*x^36 + 44*x^35 + 24*x^34 + 109*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 80*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 40*x^6 + 62*x^5 + 120*x^4 + 12*x^3 + 88*x^2 + x + 8, x^41 + 76*x^39 + 24*x^38 + 14*x^37 + 88*x^36 + 12*x^35 + 8*x^34 + 61*x^33 + 8*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 80*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 112*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 88*x^6 + 14*x^5 + 24*x^4 + 108*x^3 + 72*x^2 + 81*x + 72, x^41 + 76*x^39 + 28*x^38 + 86*x^37 + 116*x^36 + 60*x^35 + 100*x^34 + 5*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 22*x^5 + 20*x^4 + 28*x^3 + 68*x^2 + 89*x + 44, x^41 + 76*x^39 + 16*x^38 + 62*x^37 + 80*x^36 + 108*x^35 + 48*x^34 + 45*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 62*x^5 + 80*x^4 + 76*x^3 + 48*x^2 + 65*x + 112, x^41 + 76*x^39 + 116*x^38 + 6*x^37 + 12*x^36 + 28*x^35 + 108*x^34 + 117*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 70*x^5 + 108*x^4 + 124*x^3 + 12*x^2 + 73*x + 116, x^41 + 76*x^39 + 28*x^38 + 22*x^37 + 116*x^36 + 60*x^35 + 100*x^34 + 69*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 86*x^5 + 20*x^4 + 28*x^3 + 68*x^2 + 25*x + 44, x^41 + 76*x^39 + 104*x^38 + 14*x^37 + 40*x^36 + 76*x^35 + 56*x^34 + 125*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 20*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 114*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 40*x^6 + 14*x^5 + 104*x^4 + 44*x^3 + 120*x^2 + 17*x + 120, x^41 + 76*x^39 + 96*x^38 + 94*x^37 + 44*x^35 + 96*x^34 + 77*x^33 + 64*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 116*x^21 + 40*x^19 + 64*x^18 + 82*x^17 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 94*x^5 + 12*x^3 + 96*x^2 + 97*x + 64, x^41 + 76*x^39 + 112*x^38 + 62*x^37 + 80*x^36 + 44*x^35 + 80*x^34 + 109*x^33 + 112*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 62*x^5 + 80*x^4 + 12*x^3 + 80*x^2 + x + 112, x^41 + 76*x^39 + 56*x^38 + 126*x^37 + 40*x^36 + 108*x^35 + 8*x^34 + 109*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 126*x^5 + 104*x^4 + 76*x^3 + 72*x^2 + x + 88, x^41 + 76*x^39 + 72*x^38 + 62*x^37 + 24*x^36 + 108*x^35 + 120*x^34 + 45*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 62*x^5 + 88*x^4 + 76*x^3 + 56*x^2 + 65*x + 104, x^41 + 76*x^39 + 56*x^38 + 126*x^37 + 72*x^36 + 108*x^35 + 72*x^34 + 109*x^33 + 56*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 16*x^22 + 52*x^21 + 112*x^20 + 40*x^19 + 112*x^18 + 18*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 120*x^6 + 126*x^5 + 8*x^4 + 76*x^3 + 8*x^2 + x + 120, x^41 + 76*x^39 + 96*x^38 + 110*x^37 + 16*x^36 + 76*x^35 + 64*x^34 + 29*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 110*x^5 + 16*x^4 + 44*x^3 + 64*x^2 + 49*x + 80, x^41 + 76*x^39 + 92*x^38 + 118*x^37 + 52*x^36 + 60*x^35 + 100*x^34 + 101*x^33 + 12*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 54*x^5 + 84*x^4 + 28*x^3 + 68*x^2 + 57*x + 44, x^41 + 76*x^39 + 100*x^38 + 22*x^37 + 44*x^36 + 60*x^35 + 92*x^34 + 69*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 86*x^5 + 12*x^4 + 28*x^3 + 124*x^2 + 25*x + 116, x^41 + 76*x^39 + 12*x^38 + 86*x^37 + 4*x^36 + 60*x^35 + 116*x^34 + 5*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 22*x^5 + 36*x^4 + 28*x^3 + 84*x^2 + 89*x + 28, x^41 + 76*x^39 + 48*x^38 + 78*x^37 + 64*x^36 + 76*x^35 + 48*x^34 + 61*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 32*x^22 + 20*x^21 + 104*x^19 + 32*x^18 + 114*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 48*x^6 + 78*x^5 + 64*x^4 + 44*x^3 + 48*x^2 + 81*x + 96, x^41 + 76*x^39 + 96*x^38 + 78*x^37 + 112*x^36 + 12*x^35 + 125*x^33 + 48*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 32*x^20 + 104*x^19 + 114*x^17 + 32*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 96*x^6 + 78*x^5 + 112*x^4 + 108*x^3 + 17*x + 48, x^41 + 76*x^39 + 100*x^38 + 118*x^37 + 12*x^36 + 60*x^35 + 92*x^34 + 101*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 54*x^5 + 108*x^4 + 28*x^3 + 124*x^2 + 57*x + 20, x^41 + 76*x^39 + 8*x^38 + 30*x^37 + 120*x^36 + 44*x^35 + 120*x^34 + 13*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 116*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 82*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 30*x^5 + 56*x^4 + 12*x^3 + 56*x^2 + 33*x + 72, x^41 + 76*x^39 + 44*x^38 + 22*x^37 + 68*x^36 + 60*x^35 + 20*x^34 + 69*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 40*x^22 + 4*x^21 + 120*x^20 + 8*x^19 + 24*x^18 + 98*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 12*x^6 + 86*x^5 + 100*x^4 + 28*x^3 + 116*x^2 + 25*x + 28, x^41 + 76*x^39 + 12*x^38 + 86*x^37 + 36*x^36 + 60*x^35 + 52*x^34 + 5*x^33 + 28*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 108*x^6 + 22*x^5 + 68*x^4 + 28*x^3 + 20*x^2 + 89*x + 60, x^41 + 76*x^39 + 40*x^38 + 94*x^37 + 88*x^36 + 108*x^35 + 24*x^34 + 13*x^33 + 104*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 94*x^5 + 24*x^4 + 76*x^3 + 88*x^2 + 33*x + 40, x^41 + 76*x^39 + 12*x^38 + 70*x^37 + 116*x^36 + 92*x^35 + 84*x^34 + 117*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 6*x^5 + 20*x^4 + 60*x^3 + 52*x^2 + 73*x + 76, x^41 + 76*x^39 + 80*x^38 + 62*x^37 + 112*x^36 + 108*x^35 + 48*x^34 + 45*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 80*x^6 + 62*x^5 + 112*x^4 + 76*x^3 + 48*x^2 + 65*x + 16, x^41 + 76*x^39 + 12*x^38 + 6*x^37 + 116*x^36 + 92*x^35 + 84*x^34 + 53*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 70*x^5 + 20*x^4 + 60*x^3 + 52*x^2 + 9*x + 76, x^41 + 76*x^39 + 124*x^38 + 70*x^37 + 68*x^36 + 92*x^35 + 100*x^34 + 117*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 8*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 120*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 92*x^6 + 6*x^5 + 100*x^4 + 60*x^3 + 68*x^2 + 73*x + 124, x^41 + 76*x^39 + 84*x^38 + 22*x^37 + 60*x^36 + 60*x^35 + 108*x^34 + 69*x^33 + 4*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 86*x^5 + 28*x^4 + 28*x^3 + 12*x^2 + 25*x + 100, x^41 + 76*x^39 + 36*x^38 + 70*x^37 + 92*x^36 + 28*x^35 + 60*x^34 + 53*x^33 + 68*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 36*x^21 + 72*x^20 + 72*x^19 + 72*x^18 + 2*x^17 + 56*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 6*x^5 + 60*x^4 + 124*x^3 + 92*x^2 + 9*x + 36, x^41 + 76*x^39 + 28*x^38 + 102*x^37 + 100*x^36 + 28*x^35 + 68*x^34 + 21*x^33 + 60*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 56*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 72*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 38*x^5 + 4*x^4 + 124*x^3 + 36*x^2 + 105*x + 92, x^41 + 76*x^39 + 56*x^38 + 14*x^37 + 88*x^36 + 12*x^35 + 40*x^34 + 61*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 20*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 114*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 120*x^6 + 14*x^5 + 24*x^4 + 108*x^3 + 104*x^2 + 81*x + 8, x^41 + 76*x^39 + 40*x^38 + 30*x^37 + 24*x^36 + 108*x^35 + 24*x^34 + 77*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 48*x^22 + 116*x^21 + 80*x^20 + 40*x^19 + 80*x^18 + 82*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 104*x^6 + 30*x^5 + 88*x^4 + 76*x^3 + 88*x^2 + 97*x + 104, x^41 + 76*x^39 + 12*x^38 + 70*x^37 + 84*x^36 + 28*x^35 + 84*x^34 + 53*x^33 + 76*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 36*x^21 + 88*x^20 + 72*x^19 + 24*x^18 + 2*x^17 + 40*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 108*x^6 + 6*x^5 + 116*x^4 + 124*x^3 + 52*x^2 + 9*x + 108, x^41 + 76*x^39 + 116*x^38 + 70*x^37 + 108*x^36 + 28*x^35 + 44*x^34 + 53*x^33 + 116*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 36*x^21 + 40*x^20 + 72*x^19 + 104*x^18 + 2*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 20*x^6 + 6*x^5 + 76*x^4 + 124*x^3 + 76*x^2 + 9*x + 84, x^41 + 76*x^39 + 76*x^38 + 38*x^37 + 116*x^36 + 92*x^35 + 84*x^34 + 21*x^33 + 108*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 104*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 24*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 44*x^6 + 102*x^5 + 20*x^4 + 60*x^3 + 52*x^2 + 105*x + 12, x^41 + 76*x^39 + 32*x^38 + 78*x^37 + 16*x^36 + 12*x^35 + 125*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 78*x^5 + 16*x^4 + 108*x^3 + 17*x + 80, x^41 + 76*x^39 + 8*x^38 + 126*x^37 + 56*x^36 + 44*x^35 + 56*x^34 + 45*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 126*x^5 + 120*x^4 + 12*x^3 + 120*x^2 + 65*x + 72, x^41 + 76*x^39 + 28*x^38 + 6*x^37 + 4*x^36 + 28*x^35 + 68*x^34 + 117*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 70*x^5 + 36*x^4 + 124*x^3 + 36*x^2 + 73*x + 60, x^41 + 76*x^39 + 28*x^38 + 70*x^37 + 4*x^36 + 28*x^35 + 68*x^34 + 53*x^33 + 28*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 36*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 2*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 6*x^5 + 36*x^4 + 124*x^3 + 36*x^2 + 9*x + 60, x^41 + 76*x^39 + 44*x^38 + 102*x^37 + 116*x^36 + 92*x^35 + 52*x^34 + 85*x^33 + 44*x^32 + 112*x^31 + 48*x^30 + 8*x^29 + 80*x^28 + 112*x^27 + 16*x^26 + 50*x^25 + 112*x^24 + 40*x^23 + 40*x^22 + 100*x^21 + 24*x^20 + 72*x^19 + 88*x^18 + 66*x^17 + 104*x^16 + 48*x^15 + 112*x^14 + 8*x^13 + 16*x^12 + 48*x^11 + 80*x^10 + 13*x^9 + 48*x^8 + 108*x^7 + 12*x^6 + 38*x^5 + 20*x^4 + 60*x^3 + 20*x^2 + 41*x + 76, x^41 + 76*x^39 + 36*x^38 + 102*x^37 + 60*x^36 + 28*x^35 + 60*x^34 + 21*x^33 + 100*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 68*x^6 + 38*x^5 + 28*x^4 + 124*x^3 + 92*x^2 + 105*x + 68, x^41 + 76*x^39 + 112*x^38 + 62*x^37 + 48*x^36 + 44*x^35 + 16*x^34 + 109*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 62*x^5 + 48*x^4 + 12*x^3 + 16*x^2 + x + 80, x^41 + 76*x^39 + 48*x^38 + 62*x^37 + 80*x^36 + 108*x^35 + 80*x^34 + 45*x^33 + 48*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 96*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 32*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 48*x^6 + 62*x^5 + 80*x^4 + 76*x^3 + 80*x^2 + 65*x + 48, x^41 + 76*x^39 + 76*x^38 + 86*x^37 + 100*x^36 + 60*x^35 + 116*x^34 + 5*x^33 + 92*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 4*x^21 + 56*x^20 + 8*x^19 + 88*x^18 + 98*x^17 + 8*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 22*x^5 + 4*x^4 + 28*x^3 + 84*x^2 + 89*x + 124, x^41 + 76*x^39 + 100*x^38 + 38*x^37 + 60*x^36 + 92*x^35 + 60*x^34 + 21*x^33 + 36*x^32 + 112*x^31 + 16*x^30 + 8*x^29 + 112*x^28 + 112*x^27 + 48*x^26 + 50*x^25 + 80*x^24 + 40*x^23 + 56*x^22 + 100*x^21 + 8*x^20 + 72*x^19 + 72*x^18 + 66*x^17 + 120*x^16 + 48*x^15 + 80*x^14 + 8*x^13 + 48*x^12 + 48*x^11 + 112*x^10 + 13*x^9 + 16*x^8 + 108*x^7 + 4*x^6 + 102*x^5 + 28*x^4 + 60*x^3 + 92*x^2 + 105*x + 4, x^41 + 76*x^39 + 88*x^38 + 126*x^37 + 104*x^36 + 108*x^35 + 40*x^34 + 109*x^33 + 24*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 52*x^21 + 48*x^20 + 40*x^19 + 48*x^18 + 18*x^17 + 80*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 24*x^6 + 126*x^5 + 40*x^4 + 76*x^3 + 104*x^2 + x + 88, x^41 + 76*x^39 + 120*x^38 + 110*x^37 + 88*x^36 + 76*x^35 + 104*x^34 + 29*x^33 + 72*x^32 + 112*x^31 + 96*x^30 + 40*x^29 + 96*x^28 + 48*x^27 + 32*x^26 + 82*x^25 + 32*x^24 + 40*x^23 + 16*x^22 + 84*x^21 + 80*x^20 + 104*x^19 + 48*x^18 + 50*x^17 + 112*x^16 + 48*x^15 + 96*x^14 + 40*x^13 + 96*x^12 + 112*x^11 + 32*x^10 + 45*x^9 + 32*x^8 + 108*x^7 + 56*x^6 + 110*x^5 + 24*x^4 + 44*x^3 + 40*x^2 + 49*x + 8, x^41 + 76*x^39 + 84*x^38 + 54*x^37 + 28*x^36 + 124*x^35 + 44*x^34 + 101*x^33 + 100*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 68*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 34*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 118*x^5 + 124*x^4 + 92*x^3 + 76*x^2 + 57*x + 68, x^41 + 76*x^39 + 60*x^38 + 86*x^37 + 116*x^36 + 60*x^35 + 4*x^34 + 5*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 8*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 56*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 28*x^6 + 22*x^5 + 20*x^4 + 28*x^3 + 100*x^2 + 89*x + 108, x^41 + 76*x^39 + 8*x^38 + 14*x^37 + 8*x^36 + 12*x^35 + 88*x^34 + 61*x^33 + 24*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 20*x^21 + 112*x^20 + 104*x^19 + 80*x^18 + 114*x^17 + 80*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 14*x^5 + 72*x^4 + 108*x^3 + 24*x^2 + 81*x + 88, x^41 + 76*x^39 + 32*x^38 + 46*x^37 + 80*x^36 + 12*x^35 + 64*x^34 + 29*x^33 + 80*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 84*x^21 + 96*x^20 + 104*x^19 + 50*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 46*x^5 + 80*x^4 + 108*x^3 + 64*x^2 + 49*x + 80, x^41 + 76*x^39 + 84*x^38 + 86*x^37 + 124*x^36 + 60*x^35 + 108*x^34 + 5*x^33 + 68*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 8*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 56*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 116*x^6 + 22*x^5 + 92*x^4 + 28*x^3 + 12*x^2 + 89*x + 36, x^41 + 76*x^39 + 92*x^38 + 22*x^37 + 52*x^36 + 60*x^35 + 36*x^34 + 69*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 4*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 98*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 86*x^5 + 84*x^4 + 28*x^3 + 4*x^2 + 25*x + 108, x^41 + 76*x^39 + 28*x^38 + 54*x^37 + 116*x^36 + 60*x^35 + 36*x^34 + 37*x^33 + 76*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 24*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 40*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 124*x^6 + 118*x^5 + 20*x^4 + 28*x^3 + 4*x^2 + 121*x + 108, x^41 + 76*x^39 + 52*x^38 + 102*x^37 + 76*x^36 + 92*x^35 + 44*x^34 + 85*x^33 + 84*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 24*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 104*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 84*x^6 + 38*x^5 + 44*x^4 + 60*x^3 + 76*x^2 + 41*x + 52, x^41 + 76*x^39 + 40*x^38 + 110*x^37 + 104*x^36 + 76*x^35 + 56*x^34 + 29*x^33 + 56*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 110*x^5 + 40*x^4 + 44*x^3 + 120*x^2 + 49*x + 120, x^41 + 76*x^39 + 20*x^38 + 38*x^37 + 108*x^36 + 92*x^35 + 76*x^34 + 21*x^33 + 52*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 40*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 88*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 52*x^6 + 102*x^5 + 76*x^4 + 60*x^3 + 108*x^2 + 105*x + 20, x^41 + 76*x^39 + 96*x^38 + 62*x^37 + 32*x^36 + 44*x^35 + 96*x^34 + 109*x^33 + 32*x^32 + 112*x^31 + 104*x^29 + 48*x^27 + 18*x^25 + 40*x^23 + 64*x^22 + 52*x^21 + 64*x^20 + 40*x^19 + 64*x^18 + 18*x^17 + 64*x^16 + 48*x^15 + 104*x^13 + 112*x^11 + 109*x^9 + 108*x^7 + 96*x^6 + 62*x^5 + 32*x^4 + 12*x^3 + 96*x^2 + x + 32, x^41 + 76*x^39 + 76*x^38 + 54*x^37 + 4*x^36 + 124*x^35 + 52*x^34 + 101*x^33 + 124*x^32 + 112*x^31 + 48*x^30 + 72*x^29 + 16*x^28 + 112*x^27 + 16*x^26 + 114*x^25 + 48*x^24 + 40*x^23 + 104*x^22 + 68*x^21 + 120*x^20 + 8*x^19 + 88*x^18 + 34*x^17 + 72*x^16 + 48*x^15 + 112*x^14 + 72*x^13 + 80*x^12 + 48*x^11 + 80*x^10 + 77*x^9 + 112*x^8 + 108*x^7 + 44*x^6 + 118*x^5 + 36*x^4 + 92*x^3 + 20*x^2 + 57*x + 28, x^41 + 76*x^39 + 100*x^38 + 54*x^37 + 12*x^36 + 60*x^35 + 92*x^34 + 37*x^33 + 52*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 104*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 88*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 4*x^6 + 118*x^5 + 108*x^4 + 28*x^3 + 124*x^2 + 121*x + 20, x^41 + 76*x^39 + 112*x^38 + 126*x^37 + 112*x^36 + 108*x^35 + 80*x^34 + 109*x^33 + 80*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 32*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 96*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 112*x^6 + 126*x^5 + 112*x^4 + 76*x^3 + 80*x^2 + x + 80, x^41 + 76*x^39 + 28*x^38 + 38*x^37 + 68*x^36 + 92*x^35 + 68*x^34 + 21*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 124*x^6 + 102*x^5 + 100*x^4 + 60*x^3 + 36*x^2 + 105*x + 124, x^41 + 76*x^39 + 80*x^38 + 110*x^37 + 32*x^36 + 12*x^35 + 16*x^34 + 93*x^33 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 64*x^20 + 104*x^19 + 96*x^18 + 50*x^17 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 110*x^5 + 32*x^4 + 108*x^3 + 16*x^2 + 113*x, x^41 + 76*x^39 + 40*x^38 + 46*x^37 + 40*x^36 + 76*x^35 + 56*x^34 + 93*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 48*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 16*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 104*x^6 + 46*x^5 + 104*x^4 + 44*x^3 + 120*x^2 + 113*x + 56, x^41 + 76*x^39 + 68*x^38 + 86*x^37 + 44*x^36 + 124*x^35 + 124*x^34 + 69*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 100*x^6 + 22*x^5 + 12*x^4 + 92*x^3 + 28*x^2 + 25*x + 116, x^41 + 76*x^39 + 84*x^38 + 102*x^37 + 76*x^36 + 92*x^35 + 76*x^34 + 85*x^33 + 20*x^32 + 112*x^31 + 80*x^30 + 8*x^29 + 48*x^28 + 112*x^27 + 112*x^26 + 50*x^25 + 16*x^24 + 40*x^23 + 88*x^22 + 100*x^21 + 104*x^20 + 72*x^19 + 40*x^18 + 66*x^17 + 24*x^16 + 48*x^15 + 16*x^14 + 8*x^13 + 112*x^12 + 48*x^11 + 48*x^10 + 13*x^9 + 80*x^8 + 108*x^7 + 116*x^6 + 38*x^5 + 44*x^4 + 60*x^3 + 108*x^2 + 41*x + 116, x^41 + 76*x^39 + 92*x^38 + 102*x^37 + 68*x^36 + 92*x^35 + 4*x^34 + 85*x^33 + 92*x^32 + 112*x^31 + 112*x^30 + 8*x^29 + 16*x^28 + 112*x^27 + 80*x^26 + 50*x^25 + 48*x^24 + 40*x^23 + 72*x^22 + 100*x^21 + 120*x^20 + 72*x^19 + 56*x^18 + 66*x^17 + 8*x^16 + 48*x^15 + 48*x^14 + 8*x^13 + 80*x^12 + 48*x^11 + 16*x^10 + 13*x^9 + 112*x^8 + 108*x^7 + 60*x^6 + 38*x^5 + 100*x^4 + 60*x^3 + 100*x^2 + 41*x + 124, x^41 + 76*x^39 + 36*x^38 + 118*x^37 + 108*x^36 + 60*x^35 + 92*x^34 + 101*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 68*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 34*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 54*x^5 + 76*x^4 + 28*x^3 + 124*x^2 + 57*x + 116, x^41 + 76*x^39 + 16*x^38 + 62*x^37 + 112*x^36 + 108*x^35 + 112*x^34 + 45*x^33 + 16*x^32 + 112*x^31 + 64*x^30 + 104*x^29 + 64*x^28 + 48*x^27 + 64*x^26 + 18*x^25 + 64*x^24 + 40*x^23 + 96*x^22 + 52*x^21 + 32*x^20 + 40*x^19 + 32*x^18 + 18*x^17 + 96*x^16 + 48*x^15 + 64*x^14 + 104*x^13 + 64*x^12 + 112*x^11 + 64*x^10 + 109*x^9 + 64*x^8 + 108*x^7 + 16*x^6 + 62*x^5 + 112*x^4 + 76*x^3 + 112*x^2 + 65*x + 16, x^41 + 76*x^39 + 24*x^38 + 30*x^37 + 72*x^36 + 44*x^35 + 40*x^34 + 13*x^33 + 120*x^32 + 112*x^31 + 96*x^30 + 104*x^29 + 32*x^28 + 48*x^27 + 32*x^26 + 18*x^25 + 96*x^24 + 40*x^23 + 80*x^22 + 116*x^21 + 112*x^20 + 40*x^19 + 48*x^18 + 82*x^17 + 16*x^16 + 48*x^15 + 96*x^14 + 104*x^13 + 32*x^12 + 112*x^11 + 32*x^10 + 109*x^9 + 96*x^8 + 108*x^7 + 88*x^6 + 30*x^5 + 8*x^4 + 12*x^3 + 104*x^2 + 33*x + 56, x^41 + 76*x^39 + 80*x^38 + 46*x^37 + 12*x^35 + 80*x^34 + 29*x^33 + 96*x^32 + 112*x^31 + 64*x^30 + 40*x^29 + 48*x^27 + 64*x^26 + 82*x^25 + 40*x^23 + 96*x^22 + 84*x^21 + 104*x^19 + 96*x^18 + 50*x^17 + 64*x^16 + 48*x^15 + 64*x^14 + 40*x^13 + 112*x^11 + 64*x^10 + 45*x^9 + 108*x^7 + 80*x^6 + 46*x^5 + 108*x^3 + 80*x^2 + 49*x + 96, x^41 + 76*x^39 + 72*x^38 + 126*x^37 + 88*x^36 + 44*x^35 + 56*x^34 + 45*x^33 + 40*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 80*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 48*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 126*x^5 + 24*x^4 + 12*x^3 + 120*x^2 + 65*x + 104, x^41 + 76*x^39 + 4*x^38 + 22*x^37 + 44*x^36 + 124*x^35 + 60*x^34 + 5*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 120*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 72*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 36*x^6 + 86*x^5 + 12*x^4 + 92*x^3 + 92*x^2 + 89*x + 116, x^41 + 76*x^39 + 72*x^38 + 62*x^37 + 56*x^36 + 44*x^35 + 120*x^34 + 109*x^33 + 8*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 8*x^6 + 62*x^5 + 120*x^4 + 12*x^3 + 56*x^2 + x + 72, x^41 + 76*x^39 + 36*x^38 + 86*x^37 + 44*x^36 + 60*x^35 + 28*x^34 + 5*x^33 + 20*x^32 + 112*x^31 + 16*x^30 + 72*x^29 + 48*x^28 + 112*x^27 + 48*x^26 + 114*x^25 + 16*x^24 + 40*x^23 + 56*x^22 + 4*x^21 + 40*x^20 + 8*x^19 + 8*x^18 + 98*x^17 + 24*x^16 + 48*x^15 + 80*x^14 + 72*x^13 + 112*x^12 + 48*x^11 + 112*x^10 + 77*x^9 + 80*x^8 + 108*x^7 + 68*x^6 + 22*x^5 + 12*x^4 + 28*x^3 + 60*x^2 + 89*x + 116, x^41 + 76*x^39 + 92*x^38 + 54*x^37 + 84*x^36 + 60*x^35 + 36*x^34 + 37*x^33 + 44*x^32 + 112*x^31 + 112*x^30 + 72*x^29 + 80*x^28 + 112*x^27 + 80*x^26 + 114*x^25 + 112*x^24 + 40*x^23 + 72*x^22 + 68*x^21 + 88*x^20 + 8*x^19 + 120*x^18 + 34*x^17 + 104*x^16 + 48*x^15 + 48*x^14 + 72*x^13 + 16*x^12 + 48*x^11 + 16*x^10 + 77*x^9 + 48*x^8 + 108*x^7 + 60*x^6 + 118*x^5 + 116*x^4 + 28*x^3 + 4*x^2 + 121*x + 76, x^41 + 76*x^39 + 8*x^38 + 46*x^37 + 40*x^36 + 12*x^35 + 88*x^34 + 29*x^33 + 120*x^32 + 112*x^31 + 32*x^30 + 40*x^29 + 32*x^28 + 48*x^27 + 96*x^26 + 82*x^25 + 96*x^24 + 40*x^23 + 112*x^22 + 84*x^21 + 48*x^20 + 104*x^19 + 80*x^18 + 50*x^17 + 16*x^16 + 48*x^15 + 32*x^14 + 40*x^13 + 32*x^12 + 112*x^11 + 96*x^10 + 45*x^9 + 96*x^8 + 108*x^7 + 72*x^6 + 46*x^5 + 104*x^4 + 108*x^3 + 24*x^2 + 49*x + 56, x^41 + 76*x^39 + 32*x^38 + 78*x^37 + 80*x^36 + 12*x^35 + 125*x^33 + 16*x^32 + 112*x^31 + 40*x^29 + 64*x^28 + 48*x^27 + 82*x^25 + 64*x^24 + 40*x^23 + 64*x^22 + 20*x^21 + 96*x^20 + 104*x^19 + 114*x^17 + 96*x^16 + 48*x^15 + 40*x^13 + 64*x^12 + 112*x^11 + 45*x^9 + 64*x^8 + 108*x^7 + 32*x^6 + 78*x^5 + 80*x^4 + 108*x^3 + 17*x + 16, x^41 + 76*x^39 + 20*x^38 + 86*x^37 + 28*x^36 + 124*x^35 + 44*x^34 + 69*x^33 + 36*x^32 + 112*x^31 + 80*x^30 + 72*x^29 + 112*x^28 + 112*x^27 + 112*x^26 + 114*x^25 + 80*x^24 + 40*x^23 + 88*x^22 + 4*x^21 + 72*x^20 + 8*x^19 + 104*x^18 + 98*x^17 + 120*x^16 + 48*x^15 + 16*x^14 + 72*x^13 + 48*x^12 + 48*x^11 + 48*x^10 + 77*x^9 + 16*x^8 + 108*x^7 + 52*x^6 + 22*x^5 + 124*x^4 + 92*x^3 + 76*x^2 + 25*x + 4, x^41 + 76*x^39 + 8*x^38 + 126*x^37 + 120*x^36 + 44*x^35 + 56*x^34 + 45*x^33 + 72*x^32 + 112*x^31 + 32*x^30 + 104*x^29 + 96*x^28 + 48*x^27 + 96*x^26 + 18*x^25 + 32*x^24 + 40*x^23 + 112*x^22 + 52*x^21 + 16*x^20 + 40*x^19 + 16*x^18 + 18*x^17 + 112*x^16 + 48*x^15 + 32*x^14 + 104*x^13 + 96*x^12 + 112*x^11 + 96*x^10 + 109*x^9 + 32*x^8 + 108*x^7 + 72*x^6 + 126*x^5 + 56*x^4 + 12*x^3 + 120*x^2 + 65*x + 8}


In [19]:
# check Lemma 6.11
# get candidates for 41 lines
def lem611Polynomials():
	R.<x>=PolynomialRing(QQ)
	cand41=getCoeffsWeaklyType2(13,[1,-117,6300])
	cand41shift=[R(list(reversed(l)))(x+1) for l in cand41]
	cand41list=[list(reversed(l.coefficients(sparse=False))) for l in cand41shift]
	return listPowerReduceOddPC(cand41list,(x+5)^25*(x-7)^3,scc417,7)

def checkLemma611():
	R.<x>=PolynomialRing(QQ)
	print "--- Candidates for char poly corresponding to 41 lines ---"
	print ""
	tic = time.time()
	cand41red=lem611Polynomials()
	toc = time.time()
	print "Time taken to compute char polys: " + str(toc-tic) + " seconds"
	print ""
	print "Candidates for char poly:"
	for i in range(len(cand41red)):
		ff=R(list(reversed(cand41red[i])))*(x+5)^25*(x-7)^3
		ms=R(ff/gcd(ff,ff.derivative()))
		print i+1, factor(ff)
	print ""
	cand41=[cand41red[i] for i in [0,1,2,3,4,5,6,7,8,9,10,12,13,14,15,16,17,18,19,20]]
	FarkasCertificates=[
	[-26642928,0,0,-26341,-4390], 
	[32108784,0,0,18832,1713], 
	[-9000,5,0,-41], 
	[0,0,0,-427982,-149845,-31263,-5561],
	[483133968,0,0,198820,22092,2454],
	[0,0,0,26648,10679,2150],
	[0,0,0,38390,15614,2995], 
	[0,0,0,-922821,-295413,-53247,-8185], 
	[356804550,0,0,188720,26961,3851], 
	[0,0,0,0,99745,50373,10481],
	[0,0,0,0,0,38250,28348,11780], 
	[2198761371082,0,0,316965325,29410745,2438199,152389,0], 
	[-3905464984,0,0,-889825,-56453,3,0], 
	[0,0,0,0,-48443,-28265,-8404],
	[1339775890,0,0,659363,82421,10302], 
	[0,0,0,0,0,-549,-603], 
	[2871696,0,0,3493,0], 
	[26404920,0,0,15610,1163,14], 
	[0,0,0,-9088,-4476,-1026],
	[0,0,0,-3873,-1613,-180]
	]
	bag=[]
	for i in range(len(cand41)):
		ff=R(list(reversed(cand41[i])))*(x+5)^25*(x-7)^3
		ms=R(ff/gcd(ff,ff.derivative()))
		g=R(ff.derivative()/gcd(ff,ff.derivative()))
		deg=ms.degree()
		f=ms+40*x^(deg-2)
		coeffs=list(reversed(f.coefficients(sparse=False)))
		gf=x^(deg-3)*R([coeffs[2],coeffs[1],coeffs[0]])
		ggf=gf(x-1)
		clist=list(reversed(ggf.coefficients(sparse=False)))
		print "------- Infeasibility of " + str(factor(ff)) + " -------"
		print ""
		tic = time.time()
		ll=getCoeffsType2(deg-1,[clist[0],clist[1],clist[2]])
		llpol=[R(list(reversed(l)))(x+1) for l in ll]
		ll2=[list(reversed(l.coefficients(sparse=False))) for l in llpol]
		bag+=[[factor(ff),listInterlaceReduce(ll2,ms)]]
		toc = time.time()
		print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
		print ""
		deg=ms.degree()
		numrows=len(bag[i][1])
		m=matrix(numrows,deg,[bag[i][1][j] for j in range(numrows)])
		gg=vector(list(reversed(g.coefficients(sparse=False))))
		print "Coefficient matrix A for interlacing char polys:"
		print m
		print ""
		mm=vector(FarkasCertificates[i])
		print "Certificate of infeasibility c:"
		print "c = " + str(mm)
		ac=mm*m.transpose()
		print "Ac >= 0: " + str(isAtLeastZero(ac))
		print "Ac = " + str(ac)
		innerprod=sum([gg[j]*mm[j] for j in range(deg)])
		print "<g,c> < 0: " + str(innerprod < 0)
		print "<g,c> = " + str(innerprod)
		print ""


# check Lemma 6.12
# (x+5)^25 *(x-7)^9 *(x-9)^4 *(x-11)*(x^2-15*x+48)
def lem612InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll=getCoeffsWeaklyType2(5,[1,-42,680])
	llshift=[R(list(reversed(l)))(x+1) for l in ll]
	lllist=[list(reversed(l.coefficients(sparse=False))) for l in llshift]
	llred=listInterlaceReduce(lllist,(x+5)*(x-7)*(x-9)*(x-11)*(x^2-15*x+48))
	return listPowerReduce(llred,(x+5)^24*(x-7)^8*(x-9)^3)


def checkLemma612():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x+5)^25 *(x-7)^9 *(x-9)^4 *(x-11)*(x^2-15*x+48))) + "  ---"
	print ""
	tic = time.time()
	llSeidelred=lem612InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,6,[llSeidelred[j] for j in range(numrows)])
	mults=vector([25,9,4,1,1,1])
	N.<sqrt33>=NumberField(x^2 - 33)
	al=(15-sqrt33)/2
	NN.<z>=PolynomialRing(N)
	froots=[-5,7,9,11,al,15-al]
	f=prod([(z-r) for r in froots])
	fbas=[NN(f/(z-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(6,6,[fbaslist[j] for j in range(6)])
	bb=mults*fbasm
	#submatrix of m without f1
	mf1=m[range(1,numrows),range(6)]
	print "Matrix A' corresponding to interlacing polynomials without f1:" 
	print mf1
	print ""
	#Farkas certificate 
	fc1=vector(list(reversed([565,620,0,0,0,0])))
	print "Certificate of warranty c for f1:"
	print "c = " + str(fc1)  
	ac = fc1*mf1.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc1[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	#submatrix of m without f2
	mf2=m[range(3)+range(4,numrows),range(6)]
	print "Matrix A' corresponding to interlacing polynomials without f2:" 
	print mf2
	print ""
	#Farkas certificate 
	fc2=vector(list(reversed([33608, 336081, 3461627, 0, 0, 8817840108])))
	print "Certificate of warranty c for f2:"
	print "c = " + str(fc2) 
	ac = fc2*mf2.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerproduct = sum([fc2[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	#submatrix of m without f1
	mf3=m[range(4)+range(5,numrows),range(6)]
	print "Matrix A' corresponding to interlacing polynomials without f3:" 
	print mf3
	print ""
	#Farkas certificate 
	fc3=vector(list(reversed([1289, 5147, 11405, 0, 0, 0])))
	print "Certificate of warranty c for f3:"
	print "c = " + str(fc3)  
	ac = fc3*mf3.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc3[j]*bb[j] for j in range(6)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""

	p=(z+5)*(z-7)*(z-9)
	f1=vector([m[0,j] for j in range(6)])
	af1=f1*fbasm^-1
	f2=vector([m[3,j] for j in range(6)])
	af2=f2*fbasm^-1
	f3=vector([m[4,j] for j in range(6)])
	af3=f3*fbasm^-1

	print "angles for f1:"
	print af1
	print "angles for f2:"
	print af2
	print "angles for f3:"
	print af3


# check Lemma 6.13
# (x+ 5)^25*(x-3)*(x-7)^6*(x-8)*(x-9)^8
def lem613InterlacingCharacteristicPolynomials():
	R.<x>=PolynomialRing(QQ)
	ll=getCoeffsWeaklyType2(4,[1,-26,240])
	llshift=[R(list(reversed(l)))(x+1) for l in ll]
	lllist=[list(reversed(l.coefficients(sparse=False))) for l in llshift]
	llred=listInterlaceReduce(lllist,(x+5)*(x-3)*(x-7)*(x-8)*(x-9))
	return listPowerReduce(llred,(x+5)^24*(x-7)^5*(x-9)^7)

def checkLemma613():
	R.<x>=PolynomialRing(QQ)
	print "--- Infeasibility of " + str(factor((x+ 5)^25*(x-3)*(x-7)^6*(x-8)*(x-9)^8)) + "  ---"
	print ""
	tic = time.time()
	llSeidelred=lem613InterlacingCharacteristicPolynomials()
	toc = time.time()
	print "Time taken to compute interlacing char polys: " + str(toc-tic) + " seconds"
	print ""
	for i in range(len(llSeidelred)):
		ff=R(list(reversed(llSeidelred[i])))*(x+5)^24*(x-7)^5*(x-9)^7
		ms=R(ff/gcd(ff,ff.derivative()))
		print i+1, factor(ff)
	print ""
	numrows=len(llSeidelred)
	m=matrix(numrows,5,[llSeidelred[j] for j in range(numrows)])
	mults=vector([25,1,6,1,8])
	froots=[-5,3,7,8,9]
	f=prod([(x-r) for r in froots])
	fbas=[R(f/(x-r)) for r in froots]
	fbaslist=[list(reversed(l.coefficients(sparse=False))) for l in fbas]
	fbasm=matrix(5,5,[fbaslist[j] for j in range(5)])
	bb=mults*fbasm
	#submatrix of m without f1
	mf1=m[range(2)+range(3,numrows),range(5)]
	print "Matrix A' corresponding to interlacing polynomials without f1:" 
	print mf1
	print "" 
	#Farkas certificate 
	fc1=vector(list(reversed([-43,-304,0,0,-133896])))
	print "Certificate of warranty c for f1:"
	print "c = " + str(fc1)  
	ac = fc1*mf1.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc1[j]*bb[j] for j in range(5)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	#submatrix of m without f2
	mf2=m[range(numrows-1),range(5)]
	print "Matrix A' corresponding to interlacing polynomials without f2:" 
	print mf2
	print "" 
	#Farkas certificate 
	fc2=vector(list(reversed([-1562,-14059,0,0,-6402648])))
	print "Certificate of warranty c for f2:"
	print "c = " + str(fc2)  
	ac = fc2*mf2.transpose()
	print "A'c >= 0: " + str(isAtLeastZero(ac))
	print "A'c = " + str(ac)
	innerprod = sum([fc2[j]*bb[j] for j in range(5)])
	print "<g,c> < 0: " + str(innerprod < 0)
	print "<g,c> = " + str(innerprod)
	print ""
	p=(x+5)*(x-7)*(x-9)
	f1=vector([m[2,j] for j in range(5)])
	af1=f1*fbasm^-1
	f2=vector([m[4,j] for j in range(5)])
	af2=f2*fbasm^-1
	print "angles for f1:"
	print af1
	print "angles for f2:"
	print af2


In [20]:
checkLemma53()

--- Candidates for char poly corresponding to 75 lines ---

Time taken to compute char poly candidates: 0.517030000687 seconds

Candidates for char poly:
1 (x - 18) * (x - 13)^4 * (x - 15)^14 * (x + 5)^56
2 (x - 14) * (x - 17)^2 * (x - 13)^4 * (x - 15)^12 * (x + 5)^56
3 (x - 13)^2 * (x - 15)^15 * (x + 5)^56 * (x^2 - 29*x + 202)
4 (x - 17) * (x - 13)^2 * (x - 15)^14 * (x + 5)^56 * (x^2 - 27*x + 178)
5 (x - 14) * (x - 15)^14 * (x + 5)^56 * (x^2 - 28*x + 191)^2
6 (x - 11) * (x - 15)^16 * (x + 5)^56 * (x^2 - 29*x + 206)
7 (x - 13) * (x - 15)^16 * (x + 5)^56 * (x^2 - 27*x + 174)
8 (x - 10) * (x - 15)^18 * (x + 5)^56

------- Infeasibility of (x - 14) * (x - 17)^2 * (x - 13)^4 * (x - 15)^12 * (x + 5)^56 -------

Time taken to compute interlacing char polys: 0.0288548469543 seconds

Coefficient matrix A for interlacing char polys:
[    1   -54  1080 -9474 30719]
[    1   -54  1080 -9466 30615]
[    1   -54  1080 -9458 30495]

Certificate of infeasibility c:
c = (1876556160, 0, 0, 257776, 1841

In [21]:
checkLemma54()

--- Infeasibility of (x - 18) * (x - 13)^4 * (x - 15)^14 * (x + 5)^56  ---

Time taken to compute interlacing char polys: 0.0148279666901 seconds

Interlacing characteristic polynomials:
1 (x - 13)^3 * (x - 15)^13 * (x + 5)^55 * (x^3 - 41*x^2 + 543*x - 2319)
2 (x - 13)^3 * (x - 15)^13 * (x + 5)^55 * (x^3 - 41*x^2 + 543*x - 2311)
3 (x - 13)^3 * (x - 15)^13 * (x + 5)^55 * (x^3 - 41*x^2 + 543*x - 2303)
4 (x - 17) * (x - 9) * (x - 13)^3 * (x - 15)^14 * (x + 5)^55

Matrix A' corresponding to interlacing polynomials without f1:
[    1   -41   543 -2311]
[    1   -41   543 -2303]
[    1   -41   543 -2295]

Certificate of warranty c:
c = (349511, 0, 0, 151)
Ac >= 0: True
Ac = (550, 1758, 2966)
<g,c> < 0: True
<g,c> = -31230

--- Infeasibility of f1 ---

Time taken to compute interlacing char polys: 3.32836103439 seconds

Interlacing characteristic polynomials:
1 (x - 9) * (x - 13)^3 * (x - 15)^12 * (x + 5)^54 * (x^3 - 42*x^2 + 573*x - 2532)
2 (x - 11) * (x - 13)^3 * (x - 15)^12 * (x + 5)^54 * 

In [22]:
checkLemma56()

--- Candidates for char poly corresponding to 95 lines ---

Time taken to compute char poly candidates: 0.611030101776 seconds

Candidates for char poly:
1 (x - 22) * (x - 17)^4 * (x - 19)^15 * (x + 5)^75
2 (x - 18) * (x - 21)^2 * (x - 17)^4 * (x - 19)^13 * (x + 5)^75
3 (x - 17)^2 * (x - 19)^16 * (x + 5)^75 * (x^2 - 37*x + 334)
4 (x - 21) * (x - 17)^2 * (x - 19)^15 * (x + 5)^75 * (x^2 - 35*x + 302)
5 (x - 18) * (x - 19)^15 * (x + 5)^75 * (x^2 - 36*x + 319)^2
6 (x - 15) * (x - 19)^17 * (x + 5)^75 * (x^2 - 37*x + 338)
7 (x - 17) * (x - 19)^17 * (x + 5)^75 * (x^2 - 35*x + 298)
8 (x - 14) * (x - 19)^19 * (x + 5)^75

------- Infeasibility of (x - 18) * (x - 21)^2 * (x - 17)^4 * (x - 19)^13 * (x + 5)^75 -------

Time taken to compute interlacing char polys: 0.0283260345459 seconds

Coefficient matrix A for interlacing char polys:
[     1    -70   1824 -20962  89607]
[     1    -70   1824 -20954  89471]
[     1    -70   1824 -20946  89319]

Certificate of infeasibility c:
c = (14218410144, 0,

In [23]:
checkLemma57()

--- Infeasibility of (x - 22) * (x - 17)^4 * (x - 19)^15 * (x + 5)^75  ---

Time taken to compute interlacing char polys: 0.0102820396423 seconds

Interlacing characteristic polynomials:
1 (x - 17)^3 * (x - 19)^14 * (x + 5)^74 * (x^3 - 53*x^2 + 919*x - 5211)
2 (x - 17)^3 * (x - 19)^14 * (x + 5)^74 * (x^3 - 53*x^2 + 919*x - 5203)
3 (x - 17)^3 * (x - 19)^14 * (x + 5)^74 * (x^3 - 53*x^2 + 919*x - 5195)
4 (x - 21) * (x - 13) * (x - 17)^3 * (x - 19)^15 * (x + 5)^74

Matrix A' corresponding to interlacing polynomials without f1:
[    1   -53   919 -5203]
[    1   -53   919 -5195]
[    1   -53   919 -5187]

Certificate of warranty c:
c = (4776043, 0, 0, 917)
Ac >= 0: True
Ac = (4892, 12228, 19564)
<g,c> < 0: True
<g,c> = -122140

--- Infeasibility of f1 ---

Time taken to compute interlacing char polys: 3.42459702492 seconds

Interlacing characteristic polynomials:
1 (x - 13) * (x - 17)^3 * (x - 19)^13 * (x + 5)^74 * (x^3 - 54*x^2 + 957*x - 5560)
2 (x - 15) * (x - 17)^3 * (x - 19)^13 * (x + 5

In [24]:
checkLemma62()

--- Candidates for char poly corresponding to 29 lines ---

Time taken to compute char poly candidates: 69.3254239559 seconds

Candidates for char poly:
1 (x - 11) * (x - 4) * (x - 5)^12 * (x + 5)^15
2 (x - 3) * (x - 5)^11 * (x + 5)^15 * (x^2 - 17*x + 68)
3 (x - 7) * (x - 3) * (x - 5)^10 * (x + 5)^15 * (x^2 - 15*x + 48)
4 (x - 7) * (x - 4) * (x - 5)^9 * (x + 5)^15 * (x^3 - 19*x^2 + 107*x - 169)
5 (x - 5)^11 * (x + 5)^15 * (x^3 - 20*x^2 + 119*x - 188)
6 (x - 4) * (x - 3) * (x - 9)^2 * (x - 5)^10 * (x + 5)^15
7 (x - 7) * (x - 5)^10 * (x + 5)^15 * (x^3 - 18*x^2 + 93*x - 128)
8 (x - 3) * (x - 7)^2 * (x - 5)^9 * (x + 5)^15 * (x^2 - 13*x + 32)
9 (x - 5)^9 * (x + 5)^15 * (x^5 - 30*x^4 + 344*x^3 - 1874*x^2 + 4823*x - 4672)
10 (x - 5)^10 * (x + 5)^15 * (x^4 - 25*x^3 + 219*x^2 - 779*x + 928)
11 (x - 7)^2 * (x - 3)^2 * (x - 5)^8 * (x + 5)^15 * (x^2 - 15*x + 52)
12 (x - 7) * (x - 5)^8 * (x + 5)^15 * (x^5 - 28*x^4 + 298*x^3 - 1500*x^2 + 3557*x - 3176)
13 (x - 8) * (x - 3) * (x - 5)^8 * (x + 5)^15 *

In [25]:
checkLemma63()

--- Infeasibility of (x - 7)^2 * (x - 5)^10 * (x + 5)^15 * (x^2 - 11*x + 16)  ---

Time taken to compute interlacing char polys: 0.12045788765 seconds

Matrix A' corresponding to interlacing polynomials without f1:
[   1  -18   96 -134  -41]
[   1  -18   96 -134  -25]
[   1  -18   96 -134   -9]
[   1  -18   96 -134    7]
[   1  -18   96 -126 -113]
[   1  -18   96 -126  -97]
[   1  -18   96 -126  -81]
[   1  -18   96 -126  -65]
[   1  -18   96 -126  -49]
[   1  -18   96 -118 -185]
[   1  -18   96 -118 -169]
[   1  -18   96 -118 -153]
[   1  -18   96 -118 -137]
[   1  -18   96 -118 -121]
[   1  -18   96 -118 -105]
[   1  -18   96 -110 -225]
[   1  -18   96 -110 -209]
[   1  -18   96 -110 -193]
[   1  -18   96 -110 -177]
[   1  -18   96 -110 -161]
[   1  -18   96 -102 -265]
[   1  -18   96 -102 -249]
[   1  -18   96 -102 -233]
[   1  -18   96 -102 -217]
[   1  -18   96  -94 -305]
[   1  -18   96  -94 -289]
[   1  -18   96  -94 -273]
[   1  -18   96  -86 -345]
[   1  -18   96  -86 -329]
[ 

In [26]:
checkLemma64()

--- Infeasibility of (x - 3) * (x - 7)^2 * (x - 5)^9 * (x + 5)^15 * (x^2 - 13*x + 32)  ---

Time taken to compute interlacing char polys: 0.616188049316 seconds

Matrix A' corresponding to interlacing polynomials without f1:
[   1  -23  186 -630  757   -3]
[   1  -23  186 -630  773  -51]
[   1  -23  186 -630  789  -99]
[   1  -23  186 -630  805 -147]
[   1  -23  186 -622  677  165]
[   1  -23  186 -622  693  117]
[   1  -23  186 -622  709   69]
[   1  -23  186 -622  725   21]
[   1  -23  186 -614  597  365]
[   1  -23  186 -614  613  285]
[   1  -23  186 -614  629  237]
[   1  -23  186 -614  645  189]
[   1  -23  186 -606  533  485]
[   1  -23  186 -606  549  405]
[   1  -23  186 -606  549  437]
[   1  -23  186 -606  565  357]
[   1  -23  186 -598  469  605]
[   1  -23  186 -598  485  525]

Certificate of warranty c for f1:
c = (0, 0, 0, -845, -703, -235)
A'c >= 0: True
A'c = (884, 916, 948, 980, 10884, 10916, 10948, 10980, 13364, 20916, 20948, 20980, 23396, 30948, 23428, 30980, 33428,

In [27]:
checkLemma65()

--- Infeasibility of (x - 7) * (x - 5)^10 * (x + 5)^15 * (x^3 - 18*x^2 + 93*x - 128)  ---

Time taken to compute interlacing char polys: 1.02905797958 seconds

Matrix A' corresponding to interlacing polynomials without f1:
[   1  -25  222 -830 1121 -137]
[   1  -25  222 -830 1121 -105]
[   1  -25  222 -830 1137 -217]
[   1  -25  222 -830 1153 -329]
[   1  -25  222 -822 1009  223]
[   1  -25  222 -822 1009  255]
[   1  -25  222 -822 1025  143]
[   1  -25  222 -822 1025  175]
[   1  -25  222 -822 1041   31]
[   1  -25  222 -822 1041   63]
[   1  -25  222 -822 1057  -49]
[   1  -25  222 -822 1073 -161]
[   1  -25  222 -814  881  695]
[   1  -25  222 -814  897  615]
[   1  -25  222 -814  913  503]
[   1  -25  222 -814  913  535]
[   1  -25  222 -814  929  423]
[   1  -25  222 -814  929  455]
[   1  -25  222 -814  945  343]
[   1  -25  222 -814  961  231]
[   1  -25  222 -806  785  975]
[   1  -25  222 -806  801  895]
[   1  -25  222 -806  817  815]
[   1  -25  222 -806  833  703]
[   1  -2

In [28]:
checkLemma66()

--- Infeasibility of (x - 3) * (x - 5)^11 * (x + 5)^15 * (x^2 - 17*x + 68)  ---

Time taken to compute interlacing char polys: 0.149724960327 seconds

Matrix A' corresponding to interlacing polynomials without f1:
[   1  -20  122 -244   93]
[   1  -20  122 -236    5]
[   1  -20  122 -236   21]
[   1  -20  122 -236   37]
[   1  -20  122 -236   53]
[   1  -20  122 -236   69]
[   1  -20  122 -228  -35]
[   1  -20  122 -228  -19]
[   1  -20  122 -228   -3]
[   1  -20  122 -228   13]
[   1  -20  122 -220  -75]
[   1  -20  122 -220  -59]
[   1  -20  122 -220  -43]
[   1  -20  122 -220  -27]
[   1  -20  122 -212 -115]
[   1  -20  122 -212  -99]
[   1  -20  122 -212  -83]
[   1  -20  122 -204 -155]
[   1  -20  122 -204 -139]
[   1  -20  122 -196 -195]
[   1  -20  122 -196 -179]
[   1  -20  122 -188 -235]

Certificate of warranty c for f1:
c = (-256444, 0, 0, -1143, -190)
A'c >= 0: True
A'c = (4778, 12354, 9314, 6274, 3234, 194, 10810, 7770, 4730, 1690, 9266, 6226, 3186, 146, 7722, 4682, 1642, 

In [29]:
checkLemma67()

--- Infeasibility of (x - 7)^2 * (x - 3)^2 * (x - 5)^8 * (x + 5)^15 * (x^2 - 15*x + 52)  ---

Time taken to compute interlacing char polys: 0.463536024094 seconds

Matrix A' corresponding to interlacing polynomials without f1:
[   1  -25  226 -890 1405 -525]
[   1  -25  226 -882 1277  -85]
[   1  -25  226 -882 1293 -165]
[   1  -25  226 -882 1309 -245]
[   1  -25  226 -874 1165  275]
[   1  -25  226 -874 1181  195]
[   1  -25  226 -874 1197  115]
[   1  -25  226 -874 1213   35]
[   1  -25  226 -866 1085  475]
[   1  -25  226 -866 1101  395]
[   1  -25  226 -866 1117  315]
[   1  -25  226 -858 1005  675]
[   1  -25  226 -858 1021  595]
[   1  -25  226 -850  925  875]
[   1  -25  226 -842  829 1155]

Certificate of warranty c for f1:
c = (0, 0, 0, 708, 507, 154)
A'c >= 0: True
A'c = (1365, 9893, 5685, 1477, 14213, 10005, 5797, 1589, 10117, 5909, 1701, 6021, 1813, 1925, 2037)
<g,c> < 0: True
<g,c> = -37663

Matrix A' corresponding to interlacing polynomials without f2:
[   1  -25  226 -89

In [30]:
checkLemma68()

--- Infeasibility of (x - 9) * (x - 5)^9 * (x + 5)^14 * (x^2 - 12*x + 31) * (x^2 - 4*x - 1)  ---

Time taken to compute interlacing char polys: 450.774503946 seconds

Matrix A' corresponding to interlacing polynomials without f1:
[     1    -25    224   -838   1013    495   -390]
[     1    -25    224   -838   1013    527   -550]
[     1    -25    224   -838   1013    591   -806]
[     1    -25    224   -834    945    843   -994]
[     1    -25    224   -834    945    875  -1090]
[     1    -25    224   -834    945    939  -1346]
[     1    -25    224   -834    977    491    -98]
[     1    -25    224   -834    977    491    -34]
[     1    -25    224   -834    977    523   -194]
[     1    -25    224   -834    977    555   -354]
[     1    -25    224   -830    877   1207  -1582]
[     1    -25    224   -830    877   1239  -1742]
[     1    -25    224   -830    877   1271  -1838]
[     1    -25    224   -830    909    759   -270]
[     1    -25    224   -830    909    791   -430]
[    

In [31]:
checkLemma69()

--- Infeasibility of (x - 4) * (x - 3) * (x - 9)^2 * (x - 5)^10 * (x + 5)^15  ---

Time taken to compute interlacing char polys: 0.0455288887024 seconds
Matrix A' corresponding to last 5 interlacing characteristic polynomials:
[   1  -16   78 -128   33]
[   1  -16   78 -120    9]
[   1  -16   78 -112  -15]
[   1  -16   78 -104  -55]
[   1  -16   78  -96  -95]

solution to nA' = (29, -464, 2262, -3600, 525):
(27, -4, 0, 6, 0)
left kernel of A':
Vector space of degree 5 and dimension 2 over Rational Field
Basis matrix:
[ 1 -2  0  2 -1]
[ 0  0  1 -2  1]

Check that the only nonnegative solutions to nA' = (29, -464, 2262, -3600, 525) are
(25, 0, 0, 2, 2), (25, 0, 1, 0, 3), and (24, 2, 0, 0, 3)

angles for f1:
(164/315, 0, 1/45, 2/5, 2/35)
angles for f2:
(18/35, 0, 1/5, 1/5, 3/35)
angles for f3:
(32/63, 0, 17/45, 0, 4/35)
angles for f4:
(1/2, 1/6, 1/5, 0, 2/15)
angles for f5:
(31/63, 1/3, 1/45, 0, 16/105)


In [32]:
checkLemma611()

--- Candidates for char poly corresponding to 41 lines ---

Time taken to compute char polys: 395.430335999 seconds

Candidates for char poly:
1 (x - 9)^4 * (x - 7)^10 * (x + 5)^25 * (x^2 - 19*x + 80)
2 (x - 12) * (x - 11) * (x - 9)^2 * (x - 7)^12 * (x + 5)^25
3 (x - 8) * (x - 11)^3 * (x - 7)^12 * (x + 5)^25
4 (x - 9)^3 * (x - 7)^9 * (x + 5)^25 * (x^4 - 35*x^3 + 447*x^2 - 2465*x + 4948)
5 (x - 9)^4 * (x - 7)^9 * (x + 5)^25 * (x^3 - 26*x^2 + 213*x - 544)
6 (x - 11) * (x - 9)^3 * (x - 7)^10 * (x + 5)^25 * (x^2 - 17*x + 64)
7 (x - 11)^2 * (x - 9)^2 * (x - 7)^10 * (x + 5)^25 * (x^2 - 15*x + 52)
8 (x - 11) * (x - 8) * (x - 9)^2 * (x - 7)^8 * (x + 5)^25 * (x^2 - 16*x + 59)^2
9 (x - 9)^5 * (x - 7)^8 * (x + 5)^25 * (x^3 - 24*x^2 + 179*x - 412)
10 (x - 11) * (x - 5) * (x - 9)^4 * (x - 7)^8 * (x + 5)^25 * (x^2 - 17*x + 68)
11 (x - 9)^4 * (x - 7)^7 * (x + 5)^25 * (x^5 - 40*x^4 + 626*x^3 - 4784*x^2 + 17829*x - 25904)
12 (x - 11) * (x - 9)^4 * (x - 7)^9 * (x + 5)^25 * (x^2 - 15*x + 48)
13 (x - 9)^4

In [33]:
checkLemma612()

--- Infeasibility of (x - 11) * (x - 9)^4 * (x - 7)^9 * (x + 5)^25 * (x^2 - 15*x + 48)  ---

Time taken to compute interlacing char polys: 4.07785797119 seconds

Matrix A' corresponding to interlacing polynomials without f1:
[     1    -37    522  -3458  10485 -11033]
[     1    -37    522  -3458  10501 -11209]
[     1    -37    522  -3458  10517 -11385]
[     1    -37    522  -3458  10533 -11529]
[     1    -37    522  -3450  10325 -10241]
[     1    -37    522  -3450  10341 -10417]
[     1    -37    522  -3450  10357 -10593]
[     1    -37    522  -3450  10357 -10561]
[     1    -37    522  -3450  10373 -10737]
[     1    -37    522  -3442  10181  -9625]
[     1    -37    522  -3442  10197  -9801]
[     1    -37    522  -3442  10197  -9769]
[     1    -37    522  -3442  10213  -9945]
[     1    -37    522  -3434  10037  -9009]
[     1    -37    522  -3434  10053  -9153]
[     1    -37    522  -3434  10069  -9297]
[     1    -37    522  -3426   9909  -8505]

Certificate of warranty c 

In [34]:
checkLemma613()

--- Infeasibility of (x - 8) * (x - 3) * (x - 7)^6 * (x - 9)^8 * (x + 5)^25  ---

Time taken to compute interlacing char polys: 0.0636179447174 seconds

1 (x - 3)^2 * (x - 7)^6 * (x - 9)^8 * (x + 5)^24
2 (x - 7)^6 * (x - 9)^7 * (x + 5)^24 * (x^3 - 15*x^2 + 63*x - 73)
3 (x - 7)^5 * (x - 9)^7 * (x + 5)^24 * (x^2 - 12*x + 31) * (x^2 - 10*x + 17)
4 (x - 5) * (x - 7)^6 * (x - 9)^7 * (x + 5)^24 * (x^2 - 10*x + 13)
5 (x - 7)^6 * (x - 9)^7 * (x + 5)^24 * (x^3 - 15*x^2 + 63*x - 57)

Matrix A' corresponding to interlacing polynomials without f1:
[   1  -22  168 -522  567]
[   1  -22  168 -514  511]
[   1  -22  168 -506  455]
[   1  -22  168 -498  399]

Certificate of warranty c for f1:
c = (-133896, 0, 0, -304, -43)
A'c >= 0: True
A'c = (411, 387, 363, 339)
<g,c> < 0: True
<g,c> = -9069

Matrix A' corresponding to interlacing polynomials without f2:
[   1  -22  168 -522  567]
[   1  -22  168 -514  511]
[   1  -22  168 -514  527]
[   1  -22  168 -506  455]

Certificate of warranty c for f2:
c = (